In [2]:
import numpy as np
import json
import os
import pandas as pd
import requests
import bs4
from lxml import html
from fake_useragent import UserAgent
import time
import re
from urllib.parse import unquote

In [3]:
def get_yelp_data(path):
    with open(path, 'r') as file:
        raw_data = file.readlines()
    raw_data = map(lambda x: x.rstrip(), raw_data)
    json_data = '[' + ','.join(raw_data) + ']'
    df = pd.read_json(json_data)
    return df

In [4]:
file_type = 'business'
#'checkin' : 'yelp_academic_dataset_checkin.json',
#'review' : 'yelp_academic_dataset_review.json', # the file size is 6.3G 
#'tip' : 'yelp_academic_dataset_tip.json',
#'user' : 'yelp_academic_dataset_user.json' # the file size is 3.3G 

path = os.path.join('..', '..', 'data/yelp_data', 'yelp_academic_dataset_' + file_type + '.json')
df = get_yelp_data(path)

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 209393 entries, 0 to 209392
Data columns (total 14 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   business_id   209393 non-null  object 
 1   name          209393 non-null  object 
 2   address       209393 non-null  object 
 3   city          209393 non-null  object 
 4   state         209393 non-null  object 
 5   postal_code   209393 non-null  object 
 6   latitude      209393 non-null  float64
 7   longitude     209393 non-null  float64
 8   stars         209393 non-null  float64
 9   review_count  209393 non-null  int64  
 10  is_open       209393 non-null  int64  
 11  attributes    180348 non-null  object 
 12  categories    208869 non-null  object 
 13  hours         164550 non-null  object 
dtypes: float64(3), int64(2), object(9)
memory usage: 22.4+ MB


In [6]:
df.head(20)

business_id                            name  \
0   f9NumwFMBDn751xgFiRbNA        The Range At Lake Norman   
1   Yzvjg0SayhoZgCljUJRF9Q               Carlos Santo, NMD   
2   XNoUzKckATkOD1hP6vghZg                         Felinus   
3   6OAZjbxqM5ol29BuHsil3w            Nevada House of Hose   
4   51M2Kk903DFYI6gnB5I6SQ         USE MY GUY SERVICES LLC   
5   cKyLV5oWZJ2NudWgqs8VZw     Oasis Auto Center - Gilbert   
6   oiAlXZPIFm2nBCt0DHLu_Q            Green World Cleaners   
7   ScYkbYNkDgCneBrD9vqhCQ    Junction Tire & Auto Service   
8   pQeaRpvuhoEqudo3uymHIQ             The Empanadas House   
9   EosRKXIGeSWFYWwpkbhNnA                  Xtreme Couture   
10  MbZMmwo-eL0Jnm_Yb9KJrA  Chinook Landscaping and Design   
11  7Dv4_HAxsxvadEsT5fxQBg     Dependable Brakes & Exhaust   
12  M_guz7Dj7hX0evS672wIwA      Chocolate Shoppe Ice Cream   
13  JjJs3o60uQCfctDjs45cmA                    Convertabath   
14  kOICO53wbOiOJcKuCgOQ3A                   Tan Las Vegas   
15  rqcOZePlVvJP9EtzldIz0w                  Desert Storage   
16  uZuh51lXu7tsrC8RAwkg1A                  Manolo Blahnik   
17  nIEhsGbw0vJuYl05bzzj6Q               Bloom & Blueprint   
18  edQoeeBFUTYGwnUSE0tGPg                        Car Guyz   
19  Vwo64kNYDjKi98gUUv4-iQ      Gateway Fit Body Boot Camp   

                                 address             city state postal_code  \
0                        10913 Bailey Rd        Cornelius    NC       28031   
1              8880 E Via Linda, Ste 107       Scottsdale    AZ       85258   
2                  3554 Rue Notre-Dame O         Montreal    QC     H4C 1P4   
3                         1015 Sharp Cir  North Las Vegas    NV       89030   
4                     4827 E Downing Cir             Mesa    AZ       85205   
5              1720 W Elliot Rd, Ste 105          Gilbert    AZ       85233   
6           6870 S Rainbow Blvd, Ste 117        Las Vegas    NV       89118   
7                    6910 E Southern Ave             Mesa    AZ       85209   
8                         404 E Green St        Champaign    IL       61820   
9           700 Kipling Avenue Etobicoke          Toronto    ON     M8Z 5G3   
10                                                Calgary    AB     T2J 2P2   
11                1110 Saw Mill Run Blvd       Pittsburgh    PA       15226   
12                     2831 Parmenter St        Middleton    WI       53562   
13  116 N Roosevelt Ave, Bldg B, Ste 124         Chandler    AZ       85226   
14                       5465 Simmons St  North Las Vegas    NV       89031   
15                       2402 Atchley Dr        Henderson    NV       89052   
16                   3131 Las Vegas Blvd        Las Vegas    NV       89109   
17               2115 E Cedar St, Unit 3            Tempe    AZ       85281   
18                        2915 Cherry Rd        Rock Hill    SC       29730   
19                       5229 S Power Rd             Mesa    AZ       85212   

     latitude   longitude  stars  review_count  is_open  \
0   35.462724  -80.852612    3.5            36        1   
1   33.569404 -111.890264    5.0             4        1   
2   45.479984  -73.580070    5.0             5        1   
3   36.219728 -115.127725    2.5             3        0   
4   33.428065 -111.726648    4.5            26        1   
5   33.350399 -111.827142    4.5            38        1   
6   36.063977 -115.241463    3.5            81        1   
7   33.393885 -111.682226    5.0            18        1   
8   40.110446  -88.233073    4.5             5        1   
9   43.624539  -79.529108    3.0            16        1   
10  50.945960 -114.037207    5.0             3        1   
11  40.406667  -80.004450    5.0             5        1   
12  43.105310  -89.510142    3.5             6        1   
13  33.303869 -111.951660    2.5            10        1   
14  36.263362 -115.179839    3.5             5        0   
15  35.952046 -115.093483    5.0             5        0   
16  36.125732 -115.167608    4.5            32   

In [7]:
session = requests.Session()
ua = UserAgent()
#headers = {'User-Agent' : str(ua.chrome), 'Connection': 'Close'}
#headers = {'User-Agent' : str(ua.chrome)}
headers = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/61.0.3163.100 Safari/537.36'}
session = requests.Session()

In [8]:
def fetch_url_from_yelp_stop_if_captcha(biz_entry):
    s = (biz_entry['name'] + ' ' + biz_entry['city']).lower().replace('&', 'and').replace('\'', '')
    s = re.sub('[^0-9a-zA-Z]+', ' ', s)
    biz_address_tail = '-'.join(s.split())
    res = session.get('https://www.yelp.ca/biz/' + biz_address_tail, headers=headers, stream=True)
    website = None
    blocked = 0
    #print(res.text)
    idx = res.text.find('/biz_redir')
    if idx > 0:
        while res.text[idx] != '=': idx += 1
        idx2 = idx
        while res.text[idx2] != '&': idx2 += 1
        website = res.text[idx + 1: idx2]
        website = unquote(website)
    
    if website is None:
        if res.text.find('<title>Yelp Captcha</title>') >= 0:
            print(res.text)
            blocked = 1
    return website, blocked

In [9]:
urls = ['http://www.therangeatlakenorman.com/', None, 'http://www.felinus.ca', None, 'https://www.usemyguyservices.com', 'http://oasisautocenter.net', None, 'http://junctiontire.net/tires-auto-repair-mesa-az', 'http://www.theempanadashouse.com', 'http://www.xtremecouture.ca', 'https://landscapingcalgary.org', None, 'http://www.chocolateshoppeicecream.com', 'http://www.convertabath.com/', None, 'http://www.desertstorage.com/henderson-nv-self-storage', 'https://www.manoloblahnik.com/in/boutiques/Wynn%20Las%20Vegas', 'http://www.bloomandblueprint.com', 'http://www.2carguyz.com', 'https://fitbodyaz.clickfunnels.com/sales-page-yelp', None, 'https://www.glendaleaz.com/glitters/', 'http://www.ncbrewsmusic.com/', 'http://www.tipsyryde.com', 'http://www.philthyphillys.com', None, None, 'http://www.hendrickmotorsofcharlotte.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, None, 'https://www.apadana.restaurant', 'https://www.iga.net/fr/recherche_de_magasin/magasin/0293-marche-d-alimentation-beck-inc', None, 'http://www.wetzels.com', 'http://www.beechmontcc.com', 'http://www.gkvapors.com', '1592058805', 'https://www.bannerhealth.com/locations/phoenix/banner-university-medical-center-family-medicine', 'http://www.thegourmetburgerco.com', 'https://www.goodyearautoservice.com/en-US/shop/PA/Pittsburgh/000901034-15206-3149', 'http://stores.disneystore.com/ca/concord/317', None, 'http://meatchix.com', None, None, None, None, 'http://www.basspro.com/', 'https://ccv.church/locations/anthem', 'https://locations.wendys.com/united-states/oh/cleveland/13939-euclid-ave.', None, None, 'http://www.bathandbodyworks.com', 'http://irenestaproom.com', 'http://hingetown.com/', 'http://www.bestitchedneedlepointshop.com', 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=1', None, 'https://www.smlentertainment.com/calgary-north/', None, None, 'http://fiveguys.com/', 'http://platinumkustomz.com/', None, 'http://locations.tccrocks.com/az/gilbert/2218-e-williams-field-rd.html', 'https://local.fedex.com/nc/charlotte/office-0746/', 'http://www.lacoste.com/us/', 'http://www.helenblakeyflowers.com/', None, 'http://localpetpgh.com', 'http://www.ocotillointernalmedicine.com', 'http://www.mpbattingcages.com', 'https://www.garageexperts.com/location/charlotte', None, 'http://redlinepromotions.com', None, 'http://stqitoronto.com', 'http://saxetheater.com/', 'http://www.sincitypartybuses.com', 'http://www.cjaycomputers.com/', None, 'http://www.visitnc.com/listings/view/52079', None, '1592059164', 'http://www.minthillbarbershop.com/', 'http://actionfurnace.ca', 'http://www.mamanapolipizza.com', 'http://www.monarichiebride.com/', 'http://www.movers4less-il.com/', '1592059211', None, 'http://darrochmotorsports.com', 'http://www.jeffersonchandler.com/?utm_medium=listing&utm_source=yelp', 'http://landing.trugreen.com/yelp?city=Champaign&state=IL&zip=61822&utm_campaign=ORGANIC&marketingpartner=9817', None, 'http://fresh.longos.com', None, None, None, 'http://www.rehabdirectives.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.tavernrestaurantgroup.com', None, None, 'https://www.pizzaville.ca', 'http://www.royalskincare.net', '1592059367', 'http://www.sugarbowlscottsdale.com/', 'http://www.vikingcleanersaz.com', 'http://www.timhortons.com/', None, None, 'http://www.shalecreekgolfclubggp.com/', None, '1592059436', 'http://store-locator.barnesandnoble.com/store/2147', 'https://www.myairtoday.com', None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-indian-school?utm_campaign=honorhealth-medical-group-indian-school&utm_medium=local&utm_source=yelp', 'http://www.marcos.com', 'http://www.sleepandwellnessctrs.com/index.php/modules-menu/2012-01-19-13-38-38/henderson', 'http://www.hotelcharlotterestaurant.com/hotel/', 'http://www.handandstone.com', 'https://www.ulta.com/stores/charlotte-nc-590', 'http://www.JesusChurch.life', 'http://www.jjspizzacle.com/', 'http://www.dennys.com', 'https://rinsenride.com', None, 'https://kulinaryaexpress.com', 'http://www.ahwatukeepeds.com/', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=100934', None, 'http://www.amegashootingsupplies.com/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, None, 'http://www.freshcoatpainters.com/charlotte', 'http://clk.atdmt.com/HBO/go/165733594/direct/01/', None, 'http://www.hottubliquidators.com', 'https://sharonmtuttle.com/', 'http://www.fleurishflowershop.ca', 'http://www.healthspringlv.net', 'http://www.torontodermatologycentre.com', 'http://chandlersymphony.com', None, None, 'http://www.zavcoffeeshop.com', None, 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=0352&s_cid=lsl0000001', 'http://www.frederickandsons.com', 'http://www.winerack.com', 'http://www.chefalyssaskitchen.com', None, 'https://www.fatmoespizzawings.com', 'http://www.shearsensationsonline.com', 'http://www.movingforwardmadison.com/', None, 'http://www.kegsteakhouse.com/en/locations/ON/toronto/esplanade-keg/', 'https://www.thethingshop.com', None, None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89128/027192/', None, None, 'https://www.target.com/sl/richland-twp-north/2262', 'http://www.fearlessmeat1.com', None, None, 'http://www.qobollabridal.com', None, 'http://www.lcbo.com', 'https://www.dayspascottsdaleaz.com', 'http://leecafesc.com', 'http://www.gofitnessnation.com', None, None, 'https://www.peoriaaz.gov/government/departments/parks-recreation-and-community-facilities/parks-and-trails/pioneer-community-park', 'http://www.nwpoolaz.com', 'http://www.cruffs.com/', 'http://dwellingsinthedesert.com', 'https://agents.allstate.com/oscar-arnold-goodyear-az.html', 'https://www.walgreens.com/locator/walgreens-1725+northport+dr-madison-wi-53704/id=2967', None, 'http://www.purelifeaz.com', None, None, None, 'http://stlouiswings.com', None, 'http://www.massageindavidson.com', 'http://www.aumspatoronto.com', 'http://www.pizzafresh.com', None, 'https://www.raynathans.com', 'http://www.docrequest.com', 'http://www.drsimms.com', None, 'http://www.pitcrewmovin.com', 'http://www.planetfitness.com/gyms/las-vegas-flamingo-nv-611?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://www.jealousyonline.com', 'http://www.communalmule.com', None, 'http://www.thebeautyboutiquewhitby.com', 'http://www.torontopolice.on.ca/museum/', 'http://www.goldstandardhomecare.com', None, 'http://www.103yoga.com', 'https://membercuts.business.site', 'https://dutchbros.com/?utm_source=goodyear&utm_medium=yelp&utm_campaign=website_goodyear', 'http://phxstreetfood.org/', None, None, 'http://www.criminalcustomz.com', None, 'http://standandstair.com', None, 'https://www.mazzeolimousine.com', 'http://dentsquad.ca', 'http://www.menchies.com', 'https://www.smalv.com/OurCenters/HealthCareCenters/Siena', 'http://mystonecreekdentist.com', 'http://www.chobuffet.com', 'http://www.pho.com/mesa-az/pho-hien', 'http://www.mrakovic.com', 'http://www.childtime.com/your-local-school/las-vegas-nv-1803/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, None, 'https://www.sonoraquest.com/find-a-location/scottsdale-scottsdale-rd-mescal/', None, None, None, None, 'https://www.meineke.com/locations/az/surprise-4338/?utm_source=yelp&utm_medium=xvc', 'https://losolivosristorante.business.site', 'http://sunfoodsupermarket.ca/', 'http://www.2uglassandtint.com', 'http://edwardsbeautycle.com', 'https://www.allmysons.com/cleveland', None, None, 'http://www.thetailwaggersclub.com/', 'https://veggiehouse702.com', '1592060496', 'https://www.mr-bills.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://olympiasweettreats.com', 'https://locations.churchs.com/az-phoenix-7235', 'http://MasterMechanicalCleveland.com', 'https://psychbc.com/locations/greater-cleveland/north-olmsted-oh', None, 'http://sevabeauty.com/locations/charlotte_nc', None, 'http://www.uncleotis.com/', None, 'https://www.scottsdaleflighttraining.com', 'http://www.charlotteorthotics.com', None, 'http://www.motherhood.com/shipping.html', '1592060654', 'http://www.shintkd.com', None, 'http://www.thebookshopaz.com/', None, 'http://wandaroche.starkhomes.com', 'http://www.lvchinatownplaza.com/event_index.htm', 'http://www.solissouthline.com', 'http://www.hairrevivalaz.com', 'http://www.pivotimage.com', 'http://kingsfamily.com/?utm_medium=referral&utm_source=yelp', None, None, 'https://www.repairngo.com', 'http://www.fountainhillsrv.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.clubpilates.com/dtphoenix/', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'https://wearernd.com', 'http://www.lcbo.com', 'http://www.skinconceptsspa.com', 'https://locations.tropicalsmoothiecafe.com/nv/henderson/10612-south-eastern-avenue', None, 'http://lvmpd.com/', None, 'http://www.pueblomedicalimaging.com', 'http://www.creditunion1.org', None, 'http://www.pjspet.com', 'http://www.menyhartplumbing.com', 'http://www.cuisinemalaya.com', None, 'http://www.truvapenv.com', 'http://www.shopmadmod.com', None, 'http://www.southwestmobility.com/', 'http://www.wendys.com', 'http://www.starbucks.com/store/9298/', '1592061020', 'http://www.liquorstorevegas.com', 'https://www.hottopic.com', 'http://rubberstampevents.com', None, 'http://www.jcsgrillhouse.ca/mississauga/', 'http://www.guyslock.com', 'https://qcontrary.com', None, 'http://www.thecatsmeow.com', 'https://www.thejoint.com/arizona/glendale/arrowhead-ranch-48016', 'http://www.fruitsnroots.com', 'https://www.maids.com/49/?utm_source=Yelp', 'http://www.td.com', 'https://www.usps.com/', None, 'http://www.airrite-supply.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, 'https://www.subarusuperstorewest.com', 'http://allinonerepairs.us/index.php/home/', 'http://www.joesautoaz.com/', 'http://edulisrestaurant.com/', 'http://www.sdil.net', 'http://www.churchs.com', 'http://www.fatbastardburrito.ca', 'http://www.dollarama.com/', 'http://www.blackod.ca', 'http://www.rupertcornelius.net', 'http://www.alliancelv.com/', 'https://harrymarshlaw.com', 'https://nergysolutions.com', 'http://www.elitefloralevents.com', 'http://www.arizonaexecutivellc.com/', None, 'http://www.dunkindonuts.com', None, None, None, 'https://www.azairtime.com/scottsdale', 'https://www.jasonsdeli.com/restaurants/henderson-deli', None, None, None, 'http://www.izumi-sushi.com', 'http://www.logoexecutives.com', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', None, 'http://climbrefuge.com/', None, 'http://asiancafe.weebly.com/', None, 'https://www.brakesplus.com', 'https://www.churrasqueiramartins.com', None, 'http://www.vernspizza.com', 'http://tatmanstowing.com', 'https://www.mbkseniorliving.com/senior-living/az/scottsdale/mcdowell-village/?utm_source=mcdowell_village&utm_campaign=yelp', 'http://www.dhtorontoairport.com/', None, 'http://www.exxon.com', 'https://www.peacockrestaurants.com', 'http://www.thehousecoffee.ca/', None, 'http://www.calgarycurlingclub.com', 'https://clevelandhabitat.org/restore/', None, 'http://www.revelsalonmadison.com', 'http://www.misterchangs.com', 'http://www.smilesforeverpgh.com', 'http://www.charlotterusse.com', 'http://www.bistrogrande.com', None, 'https://ottogelato.ca', None, 'http://twizted-manez-beauty-barber.business.site', None, 'http://uncletetsu-ca.com', 'http://www.bitesandbrewspittsburgh.com/', 'https://www.walmaneye.com', 'http://speparty.com', 'http://www.propertyclaimadjusters.com/', 'http://www.zandrus.com', 'http://www.mercedesbenzofchandler.com', 'http://www.mycasinoquest.com', 'http://concordhairbeautysalon.com', None, None, 'http://ascentdronevideo.com/', None, 'http://www.cineplex.com/theatres/theatredetails/silvercity-crossiron-mills-cinemas-xscape-entertainment-centre.aspx', None, None, 'http://www.northtaphouse.com', 'http://www.mydcdental.com', 'http://www.kadensnails.com', 'http://soulgastrolounge.com/', 'https://greenvalleyranch.sclv.com/Entertainment/Lounges-and-Bars?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://katespade.com', None, None, None, 'https://www.toronto.ca/data/parks/prd/facilities/complex/1748/index.html', 'https://newresultsmedicalweightloss.com/near-you-scottsdale-arizona/', 'http://saigonnailspa.ca', None, 'http://www.bellevuebeer.com/', None, None, 'http://trufusion.com/', 'https://www.heartwoodroastery.com', 'http://www.poshhairandspa.com', 'http://www.yankeecandle.com', '1592062044', 'http://www.footcare4you.com/', '1592062563', 'http://www.livewellpgh.com', '1592062577', 'http://www.bloombc.com/', 'https://all-season-nails-spa.business.site', 'http://acninc.com', None, 'http://www.rexall.ca/', None, None, 'http://www.brookfieldvet.ca', 'http://theflowerroom.com/', 'http://sichuanren.ca', '1592062673', 'http://www.lodidoor.com', 'https://www.zerodegreescompany.com', 'http://thaimassagepro.vegas', 'http://www.pizzanova.com/locations/markham.html', 'http://www.yelp.com/events/chandler-rockin-taco-street-fest-2', None, 'https://www.purehockey.com/store.aspx?utm_content=Pure+Hockey-Monona-WI&loc_id=85', '1592062748', 'http://www.hickoryridgefirearms.com/page8.php', 'http://www.fantasticsams.com', 'http://www.marcs.com/stores/marc-s-medina-grocery-store-44256.aspx', 'http://www.yd.com/torontoyonge-eglinton/default.aspx', 'http://www.31kitchen.com/InfoEng.php', 'http://www.wamplerapartments.com', 'http://www.enterprisecarsales.com/location/53R1/Enterprise_Car_Sales_Charlotte?mcid=iyp:277&CUR=yelp', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXWH', 'http://www.starbucks.com', 'http://www.chewchew.net', 'http://jmacnv.com', None, 'http://www.gibs.bar', 'http://www.garciasmexicanrestaurants.net/', 'http://www.bobosbarbeque.com', 'http://www.chandlerinnaz.us', None, 'http://www.crescentoralsurgery.com/', 'http://www.fivestarmovingvegas.com', None, 'http://www.she-lv.com/', '1592062917', 'http://www.platinumpaintandbody.com', 'http://www.phxfoot.com', None, 'http://www.az-insulation.com', None, 'http://www.ilovemilanos.com/', 'http://www.duckislandclub.com/', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', None, None, 'http://skippa.ca', None, '1592063032', None, None, 'http://www.spanishoaksapts.com', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.easydrinkeasygo.com', 'http://www.wayneacebusandlimo.com', None, 'https://www.marriott.com/hotels/hotel-information/restaurant/lasbr-renaissance-las-vegas-hotel/', None, None, 'http://karbking.com', None, None, 'http://cooling-az.com', 'https://anniys-massage-spa.business.site', 'http://white-oaks.com/cmswo/', 'http://www.kirstyblattner.com', None, None, None, 'http://www.gap.com?tid=gpme000290', 'http://www.cvrr.com', 'http://www.leelaecospa.com', 'http://www.leakdetectionarizona.com', None, 'http://www.dragonflyhotyoga.com/locations/middleton-west-madison-wi/', 'http://stores.partycity.com/az/goodyear/party-store-pc947.html', 'http://www.1800degrees.ca', 'http://locationsca.michaels.com/qc/saint-laurent/4967/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.chopinrestaurant.com', 'http://www.homedepot.ca', None, None, 'http://www.clemetparks.com/education/facilities/index.asp', 'http://www.bombaybuffet.ca', '1592063291', 'http://www.portagepointe.com', 'http://www.lakeeffectlaundromat.com', None, None, 'https://www.loandepot.com/msander', 'http://xmsengineering.com/', 'http://www.puntogelatotoronto.com', None, 'http://www.rudinospizza.com', 'http://www.mimiscafe.com', 'http://larkandkey.com/', 'https://www.chocolatsfavoris.com', 'http://www.myrotiplace.com', 'http://www.sdmi-lv.com', 'http://www.allcarewellness.com', 'http://www.firstclassvanlines.ca/', 'https://www.honorhealth.com/physicians/peter-ferrara', 'http://www.canyonridgephotography.com', 'http://www.trianglebenefitservices.com', None, None, 'http://www.abrazadental.com?utm_campaign=local&utm_medium=citations&utm_source=yext', 'http://www.lampsplus.com/?sourceid=SMYELPTXLKStore16&cm_mmc=YELP-SM-_-Text-_-Link-_-Store16', 'http://www.wtaetv.com', None, 'http://www.choicechiropractic.net', '1592063514', None, 'http://www.keytohealingmassage.com/', None, None, 'http://www.duquesne.org', 'http://gcglassllc.com', 'https://www.myedgecharlotte.com', 'https://www.pinnaclebankaz.com', 'http://www.johnjayautomotive.com/', 'http://www.barneys.com', 'http://www.torontocoffeeandteahouse.com/', None, None, 'http://timessquareaz.com/', 'http://www.TriPlumb.com', 'http://www.jchobbies.com', 'https://www.adencamera.com', 'http://izakayaju.com', 'http://www.jonesysclassiccleaners.com/', 'http://www.anchorbarcanada.com/square_one/', None, 'http://www.cloudcareclinics.ca', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://bikesauce.org', None, 'http://www.sears.com/stores/arizona/mesa/0001628.html', None, None, None, None, None, 'http://singletrackfactory.com', None, 'http://www.residentialREclosings.com', 'http://www.sharifian.com', None, None, '1592063785', 'http://heritageeyecare.ca/', 'http://chazandodette.com', None, 'http://www.usa-autotransport.com/Phoenix', None, 'http://www.celebritytanning.com', 'http://www.blissdentallv.com', None, None, 'http://reinholdresidential.com/shadysidecommons/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.littlecaesars.com/', None, None, 'http://www.pods.com/phoenix.aspx', 'https://combatzonepblv.com', 'http://www.arizonawalkshop.com/', 'http://drakegeneralstore.ca', None, 'http://www.redhotrobot.net', None, 'http://miragenailsandspa.webs.com', 'https://www.mgmgrand.com/en/nightlife/whiskey-down.html', None, 'http://www.asianbuffet328.com/', 'http://www.nstuffmusic.com', 'http://www.groovyshoes.ca', 'http://www.gotoguyshandyman.com', 'http://www.meltingpot.com/charlotte-lake-norman/welcome', 'http://www.space55.org', None, 'http://fahhairextensions.com', 'http://www.visionsourcewilliamfharveyod.com', None, 'http://www.eggsmart.ca', 'https://www.lvatv.com', None, 'http://www.historybygeorge.com', '1592064139', 'http://korrys.com', 'http://www.cityofhenderson.com/parks/parks/paseo_vista.php', 'http://www.revitaantiagingcenter.com/testimonials', '1592064176', None, 'http://www.santosfairview.com', None, 'http://www.switchinkitchens.com', 'http://www.littlecaesars.com', None, 'http://www.ellekayegroup.com', 'http://7eleven.ca/store-locator/33259', None, None, 'http://www.kitchengourmetaz.com', 'https://www.batteriesplus.com/store-locator/oh/northolmsted/batteries-plus-927?utm_source=yelp&utm_medium=local&storecode=927', 'https://holisticlakewood.com', 'http://www.forestnailsandspa.com', 'http://www.massagehealthcare.com', 'http://tiredoctors.com', 'http://lonespurcafe.com', 'https://www.camdenliving.com/charlotte-nc-apartments/camden-south-end', None, None, '1592064386', 'http://www.UnexpectedVenue.com', None, '1592064415', 'https://holidayinnlongueuil.com/?utm_source=yelp&utm_medium=referral', 'http://azdistilling.com/', 'http://www.bamaspgh.com', 'http://rtcsnv.com', None, 'https://ad.doubleclick.net/ddm/clk/300117429;127049113;q', 'http://www.raphaelsbeautyschool.com', 'http://liznailsrockyriver.com', 'https://www.anytimefitness.com/gyms/866/Oregon-WI-53575/?utm_source=yelp&utm_medium=local', 'http://www.bridgespreschool.com', 'http://www.genoapizza.com', 'http://essostations.com', 'http://www.completeautomotivefairview.com', 'http://www.santanoralsurgery.com', None, 'http://www.thewinkinowl.com', 'http://polishedsalons.com', 'https://magicalstarpreschool.com', 'https://www.cellularsales.com/stores/verizon-4764-s-higley-rd-gilbert-az-85297/', 'http://www.abracleaners.com', 'http://www.liveatthestetson.com', 'https://www.hilton.com/en/hotels/clebhes-embassy-suites-cleveland-beachwood/?SEO_id=YELP-ES-CLEBHES', None, 'http://zombieburlesqueshow.com/', 'https://stores.hallmark.com/nv/henderson/amys-hallmark-shop-henderson-nv-65414.html', None, None, 'http://toronto.shambhala.org/', 'https://onekickgym.com', 'http://www.nctphoenix.com', 'http://www.akirabacktoronto.com', 'https://wolfgangpuck.com/dining/lupo-by-wolfgang-puck-las-vegas/', None, 'http://www.laserenaheights.com', 'http://www.tropicalbreezefrozendrinks.com', 'https://www.choicehotels.com/north-carolina/charlotte/rodeway-inn-hotels/nc168/rates', 'http://www.bramaleatire.com', None, 'https://www.nevadainsuranceenrollment.com', None, 'https://www.goldencoastii.com', 'http://jardin-thai.com/', None, 'https://paulpaddalaw.com', 'http://vegashotwater.com', None, None, None, 'http://www.mooreauto.com', None, None, 'http://MGpatisserie.com', 'https://www.corebellawellness.com', 'http://www.heartcleaneats.com', 'http://www.hhovv.org/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.BetterThanYiaYias.com', '1592064927', 'https://www.sonoraquest.com/find-a-location/phoenix-by-appointment-only-tatum-shea/', 'http://www.jordanbowden.com?cmpid=D3ZF_BLM_0006', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://stores.jcrew.com/en/j-crew-yorkdale', 'http://www.frostgelato.com', 'http://www.dairykingsoutheuclid.com/', 'https://www.target.com/sl/willoughby/1112', 'https://www.target.com/sl/fitchburg/2106', 'http://www.excalibur.com', 'https://www.zippssportsgrills.com', 'http://theshoebox.com', None, 'http://miracleeyebrows.com/', 'http://www.biteandsip.ca', 'http://www.247acaz.com', 'http://michaelsgenuine.com', None, 'http://www.mtlebanonpubandpizza.com', None, 'http://www.ipowerweb.com', None, 'http://kidzpreschool.com/contact/mountainsedgeandsouthernhighlands', '1592065153', 'http://www.doughboyspizzawaunakee.com/', None, None, 'http://www.evildeadvegas.com', 'https://www.marriott.com/hotel-restaurants/phxdr-jw-marriott-phoenix-desert-ridge-resort-and-spa/stonegrill/5543174/home-page.mi', 'http://streetfoodapp.com/', 'https://atriumhealth.org/medical-services/childrens-services/levine-childrens-hospital', 'http://www.snowpalacecalgary.com', 'http://www.makemydoor.com', None, 'http://www.cjgenterprise.com', 'http://www.rodiworld.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.hottopic.com', 'http://www.gtavapes.com', 'https://www.fortmillderm.com', 'https://www.learningjungle.com/en-US/lone-mountain/', '1592065314', None, 'http://www.arizonafederal.org', None, 'http://www.holeeburger.com/', 'https://www.peterpiperpizza.com/locations/mesa-az/gilbert-baseline', None, 'http://onestopnutrition.com', 'http://www.thebloordalepantry.com/', 'http://www.playitagainsam.com', None, None, None, 'http://www.churchs.com', None, 'http://www.starbucks.com', None, 'http://www.muchoburrito.com', 'https://www.chezmatante.ca/fr', None, 'http://www.thebarndoorstore.com/', 'http://www.carrefourmultisports.com/', 'http://www.loicgourmet.ca', 'http://www.swedishautowerks.com', None, 'http://www.theroomaz.com', None, 'http://sushishop.com', 'http://www.kensingtonriversideinn.com', 'http://www.ghardytours.com', 'http://www.marmiteafricaine.ca/', 'http://www.rcsandbar.com', 'http://www.theaustralianaz.com', 'http://www.pctravelservice.com', '1592065589', 'https://www.global-restaurant.com', 'http://www.tfsgolf.com/', None, '1592065626', 'http://www.dunkindonuts.com', None, 'http://www.locksmithsolutionslv.com', None, 'http://www.victoriaballet.com/', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.dollartree.com/', 'http://www.perfectionistcleaningservices.co', 'http://parkerautotransport.com/', 'http://www.mrfallstree.com', 'http://premiumnailsandspa.com', 'http://www.teamtheraputix.ca/', 'http://www.wholegrainbreadco.com/', 'http://www.sweettoothfestival.com/', 'http://www.hendersonhyundai.com', 'https://www.camelbackcollision.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://www.pizzahut.com/', None, 'http://www.xpresslubecharlotte.com', None, None, None, 'http://www.momos.ca', 'http://www.brdiamondsuite.com', None, None, 'https://www.reliablerooteraz.com', 'http://www.pitaland.ca', 'http://www.ActionComicsandSports.com', 'http://www.davisbakery.net', 'http://www.riverstonetaverne.com/', 'http://www.FiveStarPM.com', 'http://www.mrmechanicofaz.com', None, 'http://www.foodlion.com', 'http://www.zombiemfg.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://emergencyfamilymovers.com', 'https://useggrestaurant.com/', 'https://www.nationalsports.com/pages/store-pickering-ontario', 'http://airkewld.com', '1592066020', None, None, None, 'http://www.lacasadecristo.com', 'http://cfnsaz.com', None, 'http://macmillanorchards.com/', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTWS', 'http://www.momskoreanfood.com', 'http://www.azpops.com/', 'http://www.mamaspizzamatthews.com', 'https://www.bannerhealth.com/locations/glendale/banner-thunderbird-surgery-center', 'http://www.starbucks.ca', None, None, 'http://www.montroseautooutlet.com', 'http://kidneypuncher.com/', 'http://www.drnoorda.com/', 'https://candrtire.com', None, None, 'http://www.bradfordclinic.com', 'http://www.theepicure.ca', None, None, None, 'http://www.timhortons.com', None, None, 'http://www.abstractahairsalon.com', 'http://hungrybeecatering.com', 'http://livingatlavie.com', 'http://www.pittsburgh-home-inspections.com/', 'https://www.finks.com/birkdale-village', 'http://www.fearsconfections.com', '1592066435', 'http://www.crossfitvenividivici.com', '1592066459', None, 'http://herbologytours.com', 'http://www.lorays.com/home', None, 'http://www.ateraspas.com', None, 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', 'https://stores.joann.com/oh/hudson/171/', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=phxch&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'https://www.seaboardbrewing.com', None, 'http://www.lavenderoldlace.com', '1592066560', 'https://www.sleepcountry.ca', None, 'http://www.picknsave.com/StoreLocator.aspx', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://newserenityspa.com', 'http://www.pesticon.com', 'http://www.sushieye.com/', None, None, None, None, 'http://www.worldoftile.net/wordpress/locations/scottsdale/', None, None, 'https://fitnesstogether.com/plaza-midwood?utm_source=Yelp%20Web&utm_medium=Yelp%20Web&utm_campaign=Yelp%20Web', 'https://handy-howies-handyman-services.business.site', 'http://nataliesnailsalonlasvegas.com', 'http://fiveguys.com/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, None, None, 'http://extremepita.com', None, 'http://www.solaruniverse.com/vegas', 'http://www.securitysupplystore.ca', 'http://jackastors.com/location-map/34/', 'http://www.lakenormancottage.com', 'http://sunsetwater.net', 'http://www.loveyoubackboutique.com', 'http://www.coach.com', 'http://www.scottsdaleoralsurgery.com/', None, 'http://www.davidsonday.org', 'http://www.babypointlounge.com', 'http://www.aerushome.com', 'https://www.dtlvarts.com', '1592066878', None, None, 'https://www.uber.com', None, None, 'https://www.theskincentermd.com/cosmetic-plastic-surgery-shadyside-pittsburgh-pa', 'http://www.PrecisionWindowTint.com', None, 'http://www.juicecore.com/', 'http://locations.einsteinbros.com/az/scottsdale/6501-e-greenway-pkwy-bldg-5.html?utm_source=storelocator', 'http://jewelrycitylasvegas.com', 'http://heartlakeauto.net', 'http://www.mcclurecollision.com/', 'http://canyonmidwifery.com', None, None, 'http://www.superstore.ca', 'http://www.atlascinemas.net', 'http://www.fosterinn.com', 'http://5two3.com', None, 'http://www.girlsgolfofphoenix.org', 'http://www.asu.edu/news/forthemedia/asufacts/campuses.htm', 'http://igniteglassandgifts.com', 'http://www.fixsys.ca', 'http://www.skydivelasvegas.com', None, None, 'http://guildresto.com/', 'http://www.focusbenefits.com', 'http://smokespoutinerie.com', None, 'http://www.jcprinting.net', 'http://www.passautos.net', 'http://www.papagiuseppes.com/', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.salonbellarouge.com', 'https://my.clevelandclinic.org', 'http://www.littlecaesars.com/', 'http://www.graciebarra.com/ahwatukee-az', 'http://www.marahselegantbridal.com', None, 'http://albertaballet.com', None, 'http://www.eyebrows4us.com', None, 'https://familydentistryofharrisburg.com', '1592067261', 'http://lenasrotianddoubles.ca', None, None, 'http://www.aquasystems.ca/', '1592067298', 'http://www.limoluxusa.com/', None, 'https://stores.cartier.com/united-states/nv/las-vegas/3131-las-vegas-blvd-south', None, 'https://www.reliablecouriers.com/service-area/arizona/phoenix', 'http://www.theoperahousetoronto.com', 'http://www.pinkberry.com/stores/15324', 'http://facejuvenate.com', None, 'http://www.tooltimehandymanservices.com', 'http://www.concordcustomcleaners.com', None, None, 'http://www.iriefoodjoint.com/', 'http://www.laherradero.com', 'http://www.insuremedave.com?cmpid=ram6_blm_0006', None, 'https://www.caseys.com/general-store/wi-de-forest/602-w-north-st/1936?utm_campaign=website&utm_term=organic&utm_medium=referral&utm_source=yelp&utm_content=1936', None, 'https://www.services.gov.on.ca/services/mapLocations.do?action=m', 'http://www.illinipubcycle.com', 'http://www.automotivespecialtyservices.com', None, 'http://mcmanusandcampbellhair.com', 'http://www.lv-pm.com', 'http://www.brunswickvolkswagen.com', 'http://www.tempe.gov/museum', 'http://www.firstchoicedental.com/locations/east-madison-office', None, 'https://smp-ink.com', 'http://www.lilliasdressmaking.com', 'http://www.firstcareclinic.org', 'http://www.redrockcanyonlv.org/hikes-trails/first-creek-canyon', None, 'http://www.discount-drugmart.com', 'http://rumrunnervegas.com/', 'http://www.starbucks.com/', None, None, 'http://thebco.com', 'http://www.oldworldbrewery.com', None, None, None, 'https://www.mattressfirm.com/stores/az/scottsdale/mattress-stores-scottsdale-az-85260-2922.html', None, 'https://www.walmart.com/store/1380/las-vegas-nm/details', None, None, None, 'http://www.flashtelwireless.com', 'http://www.hornekia.com', None, 'http://www.yogurtology.com', None, 'http://www.iliosnoche.com', '1592067721', None, None, None, 'http://baycathospital.com/', 'http://www.sportinglife.ca/', 'http://www.montebellasalon.com', 'http://www.salvationarmyusa.org', 'http://www.crossfitmecklenburg.com', 'http://Jjsgrubbshacknliquor.com', 'http://10minuteoilchangers.business.site', 'http://www.pizzacafe.ca', 'https://www.theneckandbackclinics.com/locations/southwest-las-vegas', None, None, 'http://nextgenelectrical.com', None, None, '1592067863', None, 'http://www.clarkcountynv.gov/Depts/parks/Pages/charlie-frias-park.aspx', None, None, 'http://www.dunkindonuts.com', 'http://www.shopnofrills.ca', 'http://santemedical.ca/', None, 'http://3rdphazebodyoil.net', 'http://www.mogowestlake.com/', 'https://www.23twelveluxe.com', 'http://painting.vegas', 'https://locations.rallys.com/az/tempe/1410-west-university', 'http://www.swisschalet.com', 'http://www.rfadezbarberspa.com', None, 'http://www.bluedogtraining.com', 'http://www.brueggers.com/', 'https://www.fitnessworks.com/locations/dobson-rd-chandler-blvd', '1592068059', 'http://www.freskamediterraneangrill.com/', 'https://www.choicehotels.com/pennsylvania/gibsonia/quality-inn-hotels/pa122/rates', None, None, None, 'http://www.coyoacangrill.com', 'http://www.dobsonspringsapartments.com', None, 'https://sites.google.com/site/brightcleantollesonlaundromat/', None, 'http://www.ihg.com/candlewood/hotels/us/en/tempe/phxbr/hoteldetail', 'http://www.guerlain.com', None, 'https://www.usps.com/', 'http://www.acelebritylimousine.com', 'http://www.laserspecialists.net', 'http://vegasstronglocksmithlv.com', None, None, 'http://www.centremecanix.com', 'http://www.schmitzdoor.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.fourturnberryplace.com/', None, None, 'http://www.lassendas.com', 'http://www.UnitedBloodServicesAZ.org', 'http://www.wildburger.ca', 'https://www.pizzadivinoaz.com', None, 'http://www.chicagojoesrestaurant.com', 'http://flopatio.com/', 'http://www.undrcard.com', 'https://www.cherrylash.com', 'http://restaurants.quiznos.ca/on/mississauga/CLARKSonCROSSING-L5J2Y4', 'http://www.kitcabinets.com', None, 'http://www.nevadaozone.com/', 'http://www.arizonaturnergroup.com', 'http://samwanna.com/', 'https://www.phxfray.com', 'http://www.azdonutco.com/', 'http://www.mtnroadcycles.com', 'http://www.martinisandmagicshow.com', 'http://www.ghhlasvegas.com', None, 'http://www.tradeinautobrokers.com', 'http://www.enterprisecarsales.com/location/39R2/Enterprise_Car_Sales_Bedford?mcid=iyp:277&CUR=yelp', 'https://local.biglots.com/az/tempe/4604?zcp=pd_local_yelp', None, 'https://tonysgaragelv.com', None, 'http://www.papajohns.com', None, 'http://www.searshomeapplianceshowroom.com/locations/phoenix-az', None, None, None, 'http://www.hivehealinghouse.com', 'http://americansprinklerlandscape.com', 'http://www.ckdesignslv.com', 'http://www.lasvegasoralsurgery.com', 'https://www.signaturestyle.com/locations/on/markham/first-choice-haircutters-51352.html', None, 'http://poopertrooperslv.com', None, 'https://www.charlottebraces.com/davidson-office-location', 'http://www.josephiarussi.com', 'http://www.yankeecandle.com', None, 'https://www.369bugs.com', None, None, None, None, '1592068718', 'http://www.frysfood.com/', None, None, 'https://www.lasvegassedation.com', 'https://vitospizzaglendale.com', 'https://www.amazinglashstudio.com/studios/az/phoenix/phoenix-ahwatukee', 'https://www.azpulm.com', '1592068798', 'http://www.cedarbraemall.ca', None, 'http://megansframing.com/', None, 'http://www.summitapartmenthomes.com', 'http://www.vegasgarageco.com', 'http://www.terroni.com/bar-centrale/', 'https://www.windsorstore.com/blogs/store-locator/nv-henderson-henderson-galleria-at-sunset', None, 'http://www.snaponoptics.com', None, 'http://rockinsul.com', 'http://www.thescottsdaleresort.com/restaurants/palm_court/', 'http://www.salsablancagrill.com', 'http://www.acupuncturevegas.com', 'http://www.blvdfoodcourt.com', 'http://www.drwiner.com/', None, None, 'https://lasvegasbankruptcylawyer.co', 'http://www.celebritytanning.com', '1592069006', 'http://beststripclublasvegas.com', 'http://www.hometastingroom.ca', 'http://www.clubredrocks.com/', 'http://greaterthancoffee.com', 'http://www.caferio.com/', None, 'http://www.MountainsideAir.com', 'http://adrenalinerushslingshot.com', None, 'https://www.take5oilchange.com/locations/oh/southeuclid-140/', 'http://www.pizzahut.com/', 'http://www.micabeauty.com', 'https://www.zeppestavern.com', 'http://www.woodworkerssource.com', None, 'https://www.steammaxx.net', 'http://www.arizonaveterinaryoncology.com', 'http://newellfarmersmarket.com/', 'http://www.theheadquarters.ca', None, 'http://www.sunrisekidsdental.com/', 'http://www.azprecisionpet.com', 'https://store.401games.ca', 'http://www.meineke.com/locations/il', 'http://medpost.com/location/surprise-az', None, None, 'http://www.wickedpixiehair.com', 'http://www.poorlittlerichgirlresale.com', 'http://www.karenwrightins.com?cmpid=G2LN_BLM_0006', 'https://lesliescleaningservice.wordpress.com', 'http://www.sacredseed.com', 'http://fiveguys.com/', 'http://www.raginuptown.com/', 'http://www.meadowspediatrics.org', 'https://www.sprint.com/storefronts/bd/sprint-pittsburgh-pa-15235-fcs-102/?ecid=SEO:Yelp:2020_Q1:LastMile', None, 'https://www.wokwithmingchinese.com', 'http://mdcpgh.com/', None, 'http://www.moochieandco.com', 'http://www.coronalandscape.com', 'http://www.devourphoenix.com', None, 'http://www.vegasvacuumsewing.com', '1592069417', None, 'http://www.rossstores.com', None, 'http://www.abercrombie.com', 'https://www.homedepot.com/l/Tempe-K/AZ/Tempe/85283/489?cm_mmc=seo-yelp&', 'http://www.framezillapgh.com/', 'http://carguyscanada.ca', 'https://www.enterprise.com/en/car-rental/locations/us/al/huntsville-madison-55ha.html?mcid=iyp:8368400', None, None, 'https://www.fyhanimalhospital.org', 'http://burritozone.ca/', 'http://www.malayakitchen.com', None, 'https://www.choicehotels.com/CN478?mc=blypypaf', '1592069575', 'https://clearviewplumbing.ca', 'http://www.azvalleydental.com', 'http://www.hiddencoveapartments.com', 'http://platinumhealth.ca', 'http://www.rachellallen.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'https://www.jerseymikes.com/3141', 'http://www.rexall.ca/', None, 'http://www.seah.ca', None, 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', None, 'https://www.kohls.com/stores/oh/stow-331.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', None, None, None, None, 'http://www.starbucks.com/store/9334/', None, 'http://pamperedhair.com', 'http://www.31kitchen.com', 'http://www.acsmartialarts.com', None, 'http://www.innovativeeyecare.net', 'https://theresortatsummerlin.com/dining/casual-dining/market-place-buffet-las-vegas/', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.mzdds.com', 'http://www.jeanniesgrooming.com', 'http://www.mobilemassagebychristina.com', 'http://www.acsm-clinic.org', 'https://www.anytimefitness.com/gyms/4149/Champaign-IL-61820/?utm_source=yelp&utm_medium=local', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.jessicahair.ca', 'http://www.teamafterburn.com', None, '1592070253', None, 'https://www.beemasterlv.com', 'https://sierraspringsdental.com', None, 'https://www.alfaromeousaofhenderson.com/contact.htm', '1592070319', 'http://www.boutiquetalulah.com', None, None, 'http://www.spirithalloween.com', 'http://www.rountreeplantation.com', 'http://www.forever21.com', 'http://serviceexpertscleveland.com/', None, 'http://suncontrollandscapes.com/', 'https://locator.bmo.com/Default.aspx?t=bb&lang=en&sid=8803', 'https://locations.wendys.com/united-states/sc/fort-mill/1800-hwy-160-w.', 'http://www.elmayarestaurante.com', None, None, 'https://www.brightnow.com/dentist-near-me/surprise-dentist/40110', 'http://www.lasvegascc.com', 'http://www.landscapeguy.net', 'https://www.cloverleafsuites.com/charlotte/', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/phoenix/phxun/hoteldetail', 'http://myInsightImaging.com/AZ', None, 'http://www.azfaccs.org', 'http://www.phoenixhairextensions.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://rodneygentry.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006430627392&ds_s_kwgid=58700000443429206&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.onearmor.com', 'http://www.opusglow.com', 'http://www.hurleybrokers.com', 'http://www.Anchoranvilcoffee.com', None, 'http://www.greatclips.com/', 'http://sahniendo.com', '1592070593', 'https://www.chevronwithtechron.com', 'https://www.rayspizzacavecreek.com', None, 'http://www.hotelblackfoot.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://wwww.outlawscavecreek.com', 'http://www.beunailsbeauty.com', 'http://www.maggiesdonuts.com', None, 'https://www.johnfloydpaintingllc.com', None, None, 'http://carstarexpress.ca/locations/toronto/', 'http://www.coyoteplumbingandrooter.com', 'http://rothrockdmd.com/', 'http://www.mcmurraystylingcenter.com', 'http://danmarpetresort.com', 'https://www.MedgausDentalCare.com', 'http://www.starbucks.com', None, 'http://www.vietnampalace.ca', None, None, 'http://advancedanklefoot.com', 'http://www.sscandycigar.com/', 'http://signaturewest.net', None, None, 'http://www.burritoboyz.ca', None, None, 'https://www.moonvalleynurseries.com/services/tree-service-nevada?utm_campaign=yelp&utm_source=yelp-nv&utm_medium=tree-care', 'http://www.majesticeyebrowthreading.com', 'https://www.devitomd.com', None, 'https://www.harveys.ca', None, None, 'http://sofiasbraids.com/', None, 'https://www.aderraapts.com', 'http://goodwillsp.org/shop/retail-stores/second-editions', None, 'https://www.mattressfirm.com/stores/az/phoenix/mattress-stores-phoenix-az-85032-7927.html', 'http://www.azdmvaz.com/', 'http://www.TheMovementDanceExperience.com', 'http://www.hurstbakery.com/', 'http://www.sacktimemattress.com', 'http://www.bedbathandbeyond.com', 'http://www.shell.us', 'http://www.tambellinisbridgeville.com', 'https://electriciansmesaaz.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700007898397760&ds_s_kwgid=58700000649767852&ds_e_adid=%7Bcreative%7D&ds_url_v=2&cmpid=ADV_PG_%5B*KeywordID*%5D', 'http://www.redkingkong.com', 'http://www.bestbuy.com', None, 'http://eatnewchina.com', None, None, None, 'http://www.lvpremierpt.com', 'http://www.osteoklinika.com', 'http://koreangrillhouse.com/yonge-bloor-location/', 'https://www.providencedental.com', 'http://www.cabana-restaurant.com', None, 'http://www.dfwfurniture.com', None, 'http://www.impbaseline.com', 'https://www.walgreens.com/locator/walgreens-2324+w+war+memorial+dr-peoria-il-61614/id=6408', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.rumbi.com', 'https://arbatrestaurant.com', None, None, '1592071168', 'http://www.marshallretailgroup.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.firehousesubs.com/locations/oh/mayfield-heights', None, 'https://www.calldunrite.com', 'http://www.childrenslearningadventure.com/', 'http://www.bankofthewest.com', 'http://www.deweyscoffee.com', 'https://mercado-negro-tapas-restaurant.business.site', 'http://dethaicuisine.com', None, None, '1592071267', 'http://locations.harristeeter.com/nc/charlotte/205/', '1592071283', 'http://www.starbucks.com/store/8167/', 'http://www.amhomeservices.ca/', 'http://www.marbleslab.ca', 'http://castlecoffeelasvegas.myrestaurantpage.website', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://bikesharetoronto.com', 'http://storelocator.pepboys.com/pepboys/stores/chandler/chandler/00735', 'http://Www.makeupbynikkip.com', None, None, 'http://www.sevenhillsdentalcenter.com', 'http://www.stclairtanningspa.com', 'http://www.ontimevegas.com', None, None, 'http://www.lasvegasdiningtours.com/', None, 'http://www.airconditioningarizona.com/', 'http://www.spayaz.com/locations/mesa-az/', 'http://www.crossfitvenividivici.com', None, None, 'http://www.oakasushihouse.com', None, None, 'http://southeastlocksmith.com/', 'http://www.arizonacharliesdecatur.com/Food-Drink/Charlies-Market-Buffet', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://atechautocenter.com/', 'https://ad.doubleclick.net/ddm/clk/434184450;236814625;f', '1592071537', None, 'http://www.bonterrafarmmarket.com', None, 'http://solobace.com/', 'https://www.popeyes.com', 'http://holidayhoundhouse.com', 'http://zebreoptique.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', None, 'https://www.ediblearrangements.ca/stores/250-7th-Ave-SW-Calgary-AB-T2P-0W6', 'http://www.kaypacha.ca', None, 'http://whasn.com', 'http://www.winners.ca', 'http://www.elsantocantina.com/', 'http://www.thehomeshopnv.com/', 'https://stores.maccosmetics.com/us/oh/westlake/262-crocker-park-blvd', 'http://www.valueplace.com', 'https://stores.jcpenney.com/pa/pittsburgh/clothing-stores-pittsburgh-pa-2263.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2263', 'http://blackchickenwinecellar.com/', 'http://www.matthewsastrology.com', 'http://www.corrados.ca', 'http://www.apple.com/fashionshow', None, 'http://www.perfectprincesscut.com/', None, 'http://www.kouski.com', None, '1592071798', 'http://www.patdees.com/', 'https://order.subway.com/Default.aspx', 'http://fiveguys.com/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTVF', 'http://smartypaws.com', '1592071848', None, 'http://reflexologypedicure.blogspot.com/', 'https://www.lhshealth.com/cedarwood-plaza/', None, 'http://www.scottssharpening.com', 'http://www.starbucks.com/store/11425/', 'http://gratifyinggrains.com', 'http://dreamconnections.com', '1592071927', None, 'http://www.actionazcomputers.com', 'http://www.sushixtra.com', 'http://www.pinevillecomputers.com', 'https://corksncrafts.com', 'http://www.pictureshowent.com/home-mesa/', None, 'https://locations.whataburger.com/az/scottsdale/2955-n-hayden-rd.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', None, 'http://www.simplebistro.com', 'http://www.jimmysbackyardbbq.com', None, None, 'http://dentistrylasvegasnv.com', 'http://fishsandwich.ca/', 'http://yoamotacos.com/woodbridge-canada/', 'https://locations.theupsstore.com/pa/pittsburgh/4885-mc-knight-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.valentinos.ca', 'https://computerrepairdoctor.com/locations/cleveland/', None, 'http://www.sugarmarmalade.com/', 'http://www.winners.ca', 'http://www.originalchimneys.com/', 'https://www.hellotech.com/us/nc/mecklenburg/charlotte', None, None, 'http://www.champaigntruetires.com', 'http://www.hokkaidoseafoodsushi.com', None, 'http://www.innerstrengthchiro.com', None, None, None, None, 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2fnv%2flas-vegas%2fmidtown&sisearchengine=1524&siproduct=BEMDT_Bus', '1592072228', 'http://www.lettysonshamrock.com', None, None, 'https://www.wyndhamhotels.com/hotel/29495?tel=18882935571&iata=00093785&cid=fe:bh:20161215:yl:pp:hawus:29495', '1592072279', 'http://charlestonantiquemall.com/', 'http://apple.ca/retail/dix30', 'http://majerles.com/goodyear/', 'http://bebosmacshack.com', None, 'http://pamperohio.com/about.php', 'http://www.baystreetvideo.com/', 'http://www.bistro2182.com', 'http://staples.ca', None, 'http://www.uhhospitals.org/locations/uh-st-john-medical-center/st-john-medical-center-emergency-room', 'https://store.vioc.com/oh/brunswick/3675-center-rd-44212-060023', None, None, 'http://www.unionhillscc.com/', 'http://brighteyespa.ca', 'http://www.cosmictreats.ca', '1592072432', 'http://stardustvapes.org', None, 'http://www.nancyscheese.com', 'http://local.fedex.com/nc/concord/SRWA/', None, 'http://www.ososkatepark.com', 'http://www.alligatorpartyrental.com/', 'https://www.photobooths-charlottenc.com', None, 'http://jovanilinens.com', 'http://www.torontopearson.com/en/parking/#%23', 'http://mrgreek.com', 'http://www.thaihana99.com', 'http://www.FlawlessBeautiAndNailBar.com', None, None, 'http://www.cashamerica.com/SUPERPAWN-stores/AZ/PHOENIX/Pho18', 'http://www.holidayinn.com/hotels/us/en/toronto/yyzct/hoteldetail', None, None, 'http://vibrantcare.com', None, 'http://www.planetfitness.com/gyms/mississauga-dundas-st-on-1431?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://www.perfumes4u.com', 'http://www.fitness19.com', '1592072690', 'http://www.brisams.com/', None, 'http://www.dmelv.com', 'http://www.picea997.com', 'http://www.les3maria.com', 'http://www.jazz28.com', 'http://www.petland.ca/store-locator', None, 'http://www.tcccollision.com', 'http://www.advantaclean.com/las-vegas-nv', None, 'http://ccshvac.net', 'https://longevitymedical.com', None, 'https://tottoriallergy.com', 'http://richsautomotive.net', None, None, 'http://tasty-n-healthy.com/', 'http://www.reesors.ca/', 'http://www.tacoshuichoaz.com', 'https://www.azcasona.net', 'http://www.diamondtaxi.ca/', 'http://www.noblewindowcleaning.com', 'https://www.holysheetsusa.com', None, 'https://livepalmvillas.com', 'http://thelodgeatgrandtetonlasvegas2.cafesplanet.com', 'https://www.autumnparkcharlotte.com', 'https://www.hubbardswim.com', 'http://www.poolsnbeyond.com', 'http://www.littlerascalsrescue.com/', 'http://cityfreshpastapgh.com', 'http://www.primeroofingaz.com', 'http://www.lasvegasendodontics.com', None, None, 'http://uspalasvegas.com', 'http://stingraysushi.com/', None, None, None, 'http://www.pelicanssnoballs.com/', 'http://lakewoodmusicacademy.com', 'http://www.snvrha.org/index.htm', 'http://eastvalleysewnvac.com', 'http://www.daysinn.com/hotels/hotel-overview?wid=ps:addppc_yelp&tel=18003291073&reg=appc-_-ylPROPP-_-00405-_-diWES&hotel_id=00405&cid=whg_di_yelp', None, 'http://sushiave.net', None, 'http://www.silvercityrestaurant.ca', 'https://www.dontdrivedirty.com/locationsandpricing/?id=904', 'http://pages.wynnlasvegas.com/showstoppers', 'https://bluelakesassistedliving.com', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://www.facetofacefotographie.com', 'http://locations.harristeeter.com/nc/concord/202/', 'http://www.crownbuilders.com', 'http://www.mississaugahonda.com', 'https://www.goodfeet.com/charlotte', 'http://doorclosingsystems.com/', '1592073208', 'http://www.expressautospot.com', 'http://www.chestnutresidence.utoronto.ca/', 'http://www.naturalmeats.org', None, 'https://www.pizzaepazzi.ca', None, None, 'https://saenz-cleaning-llc-house-cleaning-service.business.site', 'https://einsteinplumbing.com/las-vegas-nv', '1592073287', 'http://www.thegreatinflatablerace.com/las-vegas', 'http://phenixsalonsuites.com/locations-detail/?id=94', 'http://www.houndhuddle.com', 'http://www.littlecaesars.com', None, '1592073354', None, 'http://www.stripdistrictmeats.com/', None, None, 'http://www.fearlesskittyrescue.org', None, 'http://www.rollinpizzapies.com', 'http://nsbank.com/', 'http://locator.carolinas.aaa.com/locations/pineville/', None, 'http://www.fortefamilypractice.com', 'http://www.arbys.com/', None, 'http://www.beatitudeschurch.org', None, None, 'https://www.alaskaair.com', 'http://www.discounttire.com/dtcs/makeAppointmentForStore.do?sc=NVL-12&utm_source=Yelp&utm_medium=iyp&utm_campaign=YelpIYPSA', None, 'http://www.parisoptique.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7784&localechange=1', None, 'http://thebreakawaybarandgrill.com/', None, 'https://www.riteaid.com/store-details?storeNumber=11467', None, 'http://storelocator.staples.ca/stores/fr_CA/QC/Saint-Laurent/21', 'https://www.supercuts.com/locations/sc/rock-hill/manchester-village-haircuts-82206.html', 'http://www.nacvegas.com', None, 'http://www.peoriashippingservice.com', 'http://www.bravaboutique.ca', 'http://www.saffronlasvegas.com/', '1592073756', None, None, 'http://gammajeansinhomedogboarding.com', 'http://www.eternitynailsspa.com', 'http://www.foodymart.com/', 'http://www.vogue-salon-spa.com', None, None, 'http://freshco.com/stores/bloor-dundas', 'http://www.tiltedgrill.com', 'http://www.northpointeyestudio.com', 'http://www.rightbuyautosales.com', 'https://www.jiffylube.com/locations/az/tempe/1665', 'https://www.choicehotels.com/wisconsin/madison/comfort-inn-hotels/wi415/rates', 'http://www.theinsidecoup.com', 'http://www.healingroots.center', 'http://www.lululemon.com/toronto/yorkdale?cid=yelp', None, 'http://tiffanynailsandspa.ca', None, 'http://www.ivoryparade.com', 'http://shehadys.com', 'http://www.torontonorthmitsubishi.ca', 'https://www.jiffylube.com/locations/nc/cornelius/3148', 'http://www.bridalboutiqueofaz.com', None, 'http://www.portofsubs.com/', None, 'https://yorkvilles.ca', 'http://www.atmospheresalon.com/', None, 'http://www.concordtavern.com', 'http://tyndallfurniture.com', 'http://www.las-vegas-locksmith.us/', 'http://www.saharamedicalinstitute.com', 'http://3vintagechicks.com/', 'http://www.edandmarks.com', 'http://www.eatoooweebbq.com', None, 'http://www.cbdefa.com', 'http://www.kuhars.com', 'https://www.mattressfirm.com/stores/nc/charlotte/mattress-stores-charlotte-nc-28277-5684.html', None, None, 'http://www.lalalunaspa.com', 'http://www.titansgym.com/index.php?Itemid=47&view=article&id=52&option=com_content', 'http://www.quiznos.com', 'http://www.sunpenang.com', 'http://www.stevenvance.com', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', '1592074181', 'http://makerealestateeasy.com', 'https://koliequestrian.com', 'http://www.goldmedalgym.com/chandler', None, 'http://www.freckaplumbing.com', 'http://www.mamaginaspizzeria.com', 'http://www.hotwire-electric.com', '1592074242', None, None, 'https://www.littledealer.com/pages/location%20phoenix', None, 'http://www.cleanandamazing.com', None, 'http://somagrill.com', 'http://www.xtremeperformance.info/', 'https://www.discounttire.com/store/nv/henderson/s/1300?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.gabesstores.com', 'http://5-starair.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://arthurmurray.com/locations/las-vegas-west-studio', None, 'http://www.winebeercigars.com', 'https://www.dairyqueen.com/us-en/locator/Detail/2398', 'http://www.glutenzerobakery.com/', None, 'http://www.cowboyciao.com', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', 'http://www.rebel-auto.com/', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=443', 'http://salsaritas.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.shoptieoneon.com/about-us.html', 'http://remachines.com', 'http://queencityrides.com', 'http://www.mazajloungecalgary.com', 'http://hahnsurvival.com', 'http://www.charmingcharlie.com/', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'https://www.starbucks.ca', None, '1592074521', '1592074530', 'http://www.scooterinvasion.com', 'http://www.zenewicznotary.com', 'http://www.onyxtheatre.com', 'http://www.mirasnails.com', 'http://www.gostorageone.com/self_storage/Las_Vegas_NV/zip_89130/storageone_self_storage/10494', 'https://www.dahntahndonuts.com', 'http://thirdeyebodyart.com', None, None, 'http://www.cjaimnotary.com', 'https://www.smalv.com/OurCenters/HealthCareCenters/Nellis', 'http://www.sinteriordesign.com', 'https://mstarkeychiro.com', 'http://www.provocateurimages.ca/', 'http://www.newwavemarket.com', 'http://www.dentistrybydesignchampaign.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.scratchkitchenclt.com', None, 'http://www.harlemrestaurant.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://classicchinesecuisine.com', 'http://www.thepreeners.com', None, 'http://www.organicmarketplacenc.com', 'https://www.officedepot.com/storelocator/nv/las-vegas/office-depot-6761/', None, None, 'http://www.surprisespringtraining.com', None, 'http://www.pickeringtoyota.com', None, 'http://www.bonniesprings.com/', 'http://www.divasalonspa.com/', 'http://wi.madison.charmingcharlie.com/fashion_accessories_madison_wi_124.html', None, 'http://roseandcrown.com/', None, 'http://www.buffalochipsaloon.com', 'http://rainbowcinemas.ca', 'http://www.grandchinesecuisine.com', 'http://www.azcommercialproperties.info/', None, 'https://bumpandroll.com', 'http://www.springmeadowliving.com', None, 'http://www.brakeshopaz.com', 'https://www.singyourstyle.com', 'http://lajollaexpress.net', '1592074921', None, 'http://calladams.com/', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=10538&localechange=1', None, 'http://www.bulwarkpestcontrol.com', None, None, None, 'https://yourfeetfixer.com/locations/chandler/', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', None, None, 'http://www.sofashack.com', 'http://mcneelyfamilydentistry.com', 'http://www.ludexauto.com', None, 'https://www.benjerry.com/gastonia', 'http://www.timhortons.com', 'http://raffin.ca', None, None, 'http://www.freshss.ca', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006435132512&ds_s_kwgid=58700000444952194&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.goodspeedperformance.com', 'http://www.ritzcarlton.com/en/Properties/Toronto/Dining/DEQ_Lounge/Default.htm', 'http://www.thesycamoreatscottsdale.com/', 'http://www.cobsbread.com/local-bakery/kingsland-calgary', None, 'https://fratellosdeliohio.com', 'https://www.wyndhamhotels.com/hotel/11185?tel=18007606483&iata=00093785&cid=fe:tl:20170523:yl:pp:tlus:11185', None, 'http://www.desertsparkle.com', None, 'http://allcityrefrigeration.com/', 'http://www.ipl-laserhairremoval.com', None, 'http://www.monicals.com/locations/monicals-pizza-of-tolono/', '1592075253', 'https://mercedes-benz-thornhill.ca', 'https://www.simonmed.com/locations/all/simonmed_imaging___summerlin', None, 'http://www.watericemesa.com', 'http://www.swisschalet.com', None, None, 'http://acehotel.com/pittsburgh', 'http://www.restauranttranscanada.ca', None, '1592075354', 'https://www.batteriesplus.com/store-locator/az/surprise/batteries-plus-616?utm_source=yelp&utm_medium=local&storecode=616', 'http://www.pioneersand.com', 'http://www.discounttire.com/', 'http://www.jonesoptical.com', 'http://www.illsecondthatonline.com', 'https://dealer.sprint.com/experts-choice', 'http://www.veneciagastonia.com', 'https://www.greatwolf.com/concord/dining-shopping/dining/loose-moose-cottage', 'https://www.scottsdale5thapts.com', 'http://www.shanghaipalacerestaurant.ca/', None, 'http://anytimefitness.com/en-us/clubs/582', None, '1592075489', 'http://lakecityair.com', 'http://www.level20lounge.com', 'http://www.vetteculture.net', 'http://chambersphx.com/', None, None, 'http://www.jimmythegreekgroup.ca', 'http://www.element-dayspa.com/', 'http://www.shopbop.com', '1592075568', 'http://www.the505e.com/', 'http://icyroll20.com', 'http://www.verizonwireless.com/stores/arizona/surprise/surprise-319434/', 'http://www.blizzyogurt.com', None, 'http://www.mygnp.com', '1592075632', 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/etobicoke-(1).aspx', None, '1592075661', 'http://homefabricsonline.com', 'https://kayahempco.com', 'http://www.planetfitness.com/gyms/kannapolis-nc-1212?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', '1592075693', 'http://myarizonasmile.com', 'https://www.navyfederal.org/?cmpid=bn%7Cyelp%7Cevgrn%7Cbrn%7Cnull%7Cnull%7C01/13/2020%7Cml%7Cnull', 'http://www.knitandsip.com', 'http://www.carpetmdonline.com', 'http://www.slcrealty.com', None, 'http://www.gvdentalcenter.com', None, 'https://www.apple.com/ca/retail/yorkdale/', 'http://www.pizzapanorama.ca/index.html', None, None, None, None, 'https://easternarizonaexterminating.com', 'http://envoguestyle.com', None, None, 'http://www.greenvalleypres.com', 'https://www.petsuppliesplus.com/Store/OH/Middleburg-Heights/Middleburg-Heights/28?utm_source=Yelp&utm_medium=Store-Page%C3%8A', '1592075851', 'https://www.hermanheylflorist.com', 'http://arizonanationalinsurance.com', None, 'https://www.sunrisepreschools.com/locations/dysart-thomas/?utm_source=yelp&utm_campaign=online_listing_goodyear_287&utm_medium=referral&utm_term=business_url', 'http://neurocnv.com/', 'http://www.showmethatsmile.com', 'http://www.facesbylorri.com', 'http://www.qinaturalfood.com', 'http://www.longos.com/store/storedetails.aspx?store_no=10', 'https://spbarbershop.com', 'https://www.nofrills.ca/store-locator/Jerry%27s+No+Frill%27s+Mississauga/3101?storeId=3101', None, 'https://www.advantage.com/location/las-vegas-mccarran-intl-airport-las/?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_local', 'https://www.walgreens.com/locator/walgreens-133+w+8th+ave-homestead-pa-15120/id=9674', None, None, '1592076007', None, 'http://www.bikesaviours.org/', 'http://saucelv.com/', None, 'http://www.splendidchinamall.ca', 'http://www.libertytintsolutions.com', None, 'http://scottsdale.hyatt.com', 'https://www.aceofheartscpr.net/locations/ace-of-hearts-cpr-las-vegas', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'http://www.re-newcabinets.com/', 'http://www.lloydsrestaurant.ca', 'http://www.medmassage.com', None, 'http://www.familyfarmcreameries.com', 'http://www.bloomingexpressionsflowers.com/', 'https://www.valero.com', 'http://www.norwinbowl.com', 'http://www.smilestraight.com', 'http://www.sunvalleyscooters.com', 'http://www.paperjoy.com/', None, 'https://www.redclayciderworks.com', 'http://arkvegas.com/restaurants_village-streets.htm', None, None, 'http://www.martelsalon.com/', None, 'http://www.theunicornpub.com', None, 'http://www.superstarmovers.com', 'http://www.tempe.gov/parks/', 'https://shop.wirelesszone.com/ma/hudson/234-washington-street', 'http://www.phoenixcarpetrepair.com', None, None, 'http://www.fernandosmexicanrestaurant.ca', 'http://scaasports.com', 'http://www.deervalleyplumbing.com', 'http://www.nspeds.com', 'http://www.americanapparel.net', 'http://www.sahara.bhhsnv.com', 'http://www.nobutei.com/', 'http://www.marvelmasonry.com', '1592076409', 'http://store.bobbiesflowers.com/?srccode=yelp_track', None, 'http://www.cicis.com/locations/nv-las-vegas-9890-s-maryland-pkwy', 'https://www.dontdrivedirty.com/locationsandpricing/?id=907', None, 'http://www.dilisosmeats.com', None, 'http://thebacklotbar.com', 'https://palmbeachtan.com/locations/AZ/Scottsdale-North-Scottsdale-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'http://www.procarehospicenv.com', '1592076498', 'https://www.harborinnseafoodcharlotte.com', 'https://www.kohls.com/stores/pa/gibsonia-1271.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.nsbank.com/branch/?branch=durango_and_215_south_branch', None, None, None, None, '1592076576', 'http://www.paradisemedspa.com', None, None, 'http://www.torontolivings.com', 'https://www.usps.com', 'http://www.scottspro.net', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=976', 'https://www.epoxylasvegas.com', 'http://www.pappertdentistry.com/', 'http://www.amjcampbell.com', 'http://www.valleyendodontic.com', 'http://www.encorelasvegas.com/#/entertainment/sinatra_dance_with', 'https://www.target.com/sl/glendale/1806', 'https://www.ulta.com/stores/gilbert-az-354', 'http://habitburger.com', None, 'http://www.greatclips.com/salons/6225', 'http://www.heavenscookie.com/', 'http://www.coolcomfort.net', None, 'https://late-night.business.site', 'https://mydeluxecleaners.com', 'http://www.thaiexpress.ca/', 'http://brotherspizzaandwings.ca', 'http://www.thechefon2wheels.com', 'http://www.reedkrakoff.com', None, None, 'http://www.big5sportinggoods.com', 'http://www.onelovegrapplingarts.com', 'http://www.eatatjoeydeli.com', None, 'http://www.montgomeryross.ca/', 'http://intouchcoachingllc.com', 'http://www.grottoshakersquare.com', 'http://www.ddsdiscounts.com', 'http://martininailbar.com', 'http://www.wedjaz.com', 'http://www.kasecustom.com', 'http://amadioranch.com', None, 'http://www.dworksautotintanddetailing.com', 'http://www.toothhealer.com', 'http://www.chbaz.com', None, 'http://gameworldvegas.com/', 'http://hearingassociateslv.com', 'http://www.kildares.ca', 'http://www.tablewinemadison.com', 'http://oohlalash.ca', 'http://www.ezpawn.com', 'http://www.starbucks.com/store/9298/', 'http://www.gnc.com', 'http://conniesjewelrygalleryandclockshop.com/', None, 'http://www.sushikanda.com/laval.html', None, None, 'http://www.quilles440.com/index_files/Page455.htm', 'http://www.oreillyauto.com', 'http://www.maxandermas.com/locations/333038', 'http://www.abreedapartanimalhospital.com', 'http://www.harbsauto.com', 'http://www.imagepluslasvegas.com', None, None, 'http://www.karachikitchen.com/location/brampton', None, 'http://www.flikandcompany.com', 'http://Skingri-la.com', 'http://www.theperfectshadesalon.com', None, '1592077170', None, None, 'http://www.calgaryautoquest.ca', '1592077203', None, None, None, 'https://www.beautybrands.com/store-locator/ahwatukee.do', 'http://www.rochestersdining.com', None, 'http://www.riverset.com', 'http://www.alohacardiology.com', None, 'https://www.ttc.ca/Subway/Stations/Wellesley/station.jsp', 'http://www.restaurantmissitalia.com/fr', 'http://www.charliesbarkpark.com', 'http://www.heartcenterofnv.com', 'http://www.networkautomotive.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.thaidtogo.com', 'www.edelweissimports.com', 'http://www.mcnallypianomovers.com/', 'http://www.daybreaknewmarket.com', 'http://www.wealthsimple.com', None, 'http://algobertoslasvegas.onlunchroom.space', 'http://phoenixcarnival.com', 'http://cabanatanolympia.business.site', 'http://www.bayrischerhof.biz', 'http://challengeyourgame.com/', None, None, None, None, None, 'http://www.phtowers.com/', 'http://www.raniasgrill.com/', None, 'http://www.dibellas.com/club-bread?source=yelp', '1592078201', 'http://www.burritoboyz.ca', None, 'https://locations.jimmyjohns.com/oh/southeuclid/', 'http://rusanscharlotte.com', 'http://www.brooklinbakery.ca', 'http://dukepubs.ca/westminster', None, 'http://www.regmovies.com/Theatres/Theatre-Folder/Regal-Severance-Town-Center-Stadium-14-822?utm_medium=social+network&utm_source=yelp&utm_campaign=yelp+-+description&utm_term=Regal+Cinemas+Severance+Town+Center+14', 'http://www.longjohnsilvers.com/', None, 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', '1592078324', None, 'https://www.ahn.org/location-detail?name=wexford_Health_%21_Wellness_Pavilion', 'http://www.legendswarehouse.ca', None, 'http://www.gordonsjewelers.com', 'https://www.mukujapaneseramen.ca', 'http://www.kyreneinternalmedicine.com', 'https://www.presleyuptown.com', 'http://www.rapaczdental.com', 'http://www.ethicalaz.com/moquinosbodyandpaint', '1592078404', 'http://www.reesors.ca/', None, 'http://www.absorental.com', 'http://isthmustattoo.com', 'http://azhairdoctor.com', 'http://www.natalyapanchenkostudios.com', 'http://www.thrifttown.com/', 'http://www.lecharmeroses.com', None, 'https://www.northpointecle.com', None, None, 'http://robraymagic.com/', 'http://www.busybuggy.com/', 'https://www.lvhomeinspection.com', 'https://store.vioc.com/nv/las-vegas/9631-trailwood-dr-89134-HC0003', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.arsenal201.com', 'http://www.aplusnanniesinc.com', None, 'http://www.waypointvacation.ca', 'https://www.wastedgrain.com', 'http://www.analogcoffee.ca', 'http://www.chandlerneurologyandsleep.com', 'http://rockinrollssushi.com', None, 'http://www.ymcacharlotte.org', 'http://www.pohlenv.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZXR', '1592078668', 'http://www.myoworksvegas.com/', 'https://www.cottonlanecitrus.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.villagerapartments.com', None, None, None, 'https://shop.nordstrom.com/c/wedding-suite-locations-beachwood-place?utm_source=yelp&utm_medium=organic&utm_campaign=wedd&utm_content=11227&utm_channel=lcl_brand_p&sp_source=yelp&sp_campaign=wedd', 'http://vegascaralarm.com', 'http://www.lubestop.com/Locations/Solon', 'https://www.fatcatsfun.com/gilbert', 'http://www.pinnaclevistavilla.com/', 'http://hharizona.com', 'http://www.sinatralv.com', 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'http://www.mlsalonspa.com', 'http://www.xplozone.com', '1592078860', None, 'http://bodyworksplus.com', 'https://circlecentreforhealth.com', None, 'http://www.hyatt.com/gallery/torphannon/kosher.html', 'http://www.halalbiryanihouse.com', None, 'http://longoortho.com/', 'http://www.emeraldsuites.com', 'http://www.gophoit.com/index.htm', 'http://www.sherwin-williams.com/store-locator/paint-store/Charlotte/NC/2164', None, 'http://www.attentiontoautodetail.com', 'http://www.club120.ca', 'http://www.onereddoorhudson.com/', 'http://pittsburgh.pirates.mlb.com/pit/ballpark/pncpark-events/venues/brewing-hall/', None, 'http://www.sunburstsmokeshop.com', None, None, 'http://www.DrJoyceChang.com', 'http://www.adogsbestfriendlv.com', None, 'http://www.jumpforfun.com', 'http://www.gonsteadperformance.com/', 'http://www.sunkissedtanninglv.com', 'https://www.purebarre.com/location/brecksville-oh', None, 'https://www.moderntortilla.com', None, 'http://bagelnash.ca', None, 'http://www.elevationweightloss.com', 'http://www.homegoodstore.com', None, None, None, 'http://www.frenchconnection.com', 'https://thirteen55motorsports.com', None, 'http://www.biltmorelifestylesre.com', None, 'https://megafurnitureusa.com', None, 'http://brittneywinklerhair.com', 'https://www.noons.co', 'http://www.eurocarsdetail.com', None, 'http://www.nailbrite.ca', 'http://worldofbeer.com/Locations/Gilbert', 'http://smartbuyavenue.com', None, '1592079287', None, 'http://www.pawsnclawsvet.com', 'https://www.smartstyle.com/en-us/locations/nv/las-vegas/located-inside-walmart-3473-haircuts-3334.html', 'http://www.christownspectrum.com', 'http://www.rebarn.ca', 'http://www.champps.com/', None, 'http://www.thepavilionsattalkingstick.com', 'http://www.merriperry.com', 'http://www.willowsdesign.com', None, None, None, None, None, 'http://www.dollartree.com', 'http://labambaburritos.com/', None, 'https://locations.teavana.com/us/az/scottsdale/7014-east-camelback-rd.html', 'http://whiskyattic.com/', 'http://apexendolv.com', 'https://locations.dennys.ca/AB/CALGARY/248179', 'http://www.alphadrone.com', 'http://sushibarkim.com/index.php', 'https://adamsplacerestaurant.wordpress.com', None, 'http://camelbacktailoringandalterations.com', 'http://www.firedupbbq.com', 'https://calgarycanine.com/auburn-bay/', None, 'http://www.oneshotinstallation.com', 'http://donutconnection.com/', 'http://www.goodfaithcasting.com', 'https://lvccld.org', None, 'https://www.sdi.edu', 'http://www.rslcs.org', 'http://www.coinlesslaundry.com/alma-school.html', None, 'http://www.oggiristorante.net/', 'https://www.ph216.com', 'http://www.shopnsavefood.com', None, 'http://www.manchuwok.com/', 'http://billskupa.com', 'http://www.cellphonerepaircomputerrepairlasvegas.com/', 'https://www.smartstyle.com/en-us/locations/nv/north-las-vegas/located-inside-walmart-2592-haircuts-3346.html', 'http://www.zernichlaw.com', 'http://www.greatdjmusic.com', '1592079719', 'https://www.redshoeslv.com', 'http://www.brighton.com', 'http://www.breadandsalt.ca', 'http://www.verizonwireless.com/stores/ohio/westlake/westlake-202670/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://zeroissuebeer.com', 'https://www.corepoweryoga.com/free-week?utm_source=yelp&utm_medium=cta&utm_campaign=chandler-yelp-free-week', 'http://www.ljkusina.com', 'https://www.kungfutea.com', None, None, 'https://www.discounttire.com/store/az/scottsdale/s/1284?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://desertridgemusicacademy.com', 'https://www.popeyes.com', 'http://www.martislounge.com', None, None, 'http://lylesjewelryandcoin.com', '1592079878', None, 'http://www.luckyhuelv.com', None, 'http://www.colonyroofing.com', None, None, 'http://www.mentorsportsbar.com', 'https://www.randrrefrigeration.com', 'http://kaizenautocare.com/body-shop-phoenix-az/', 'http://www.dsw.com', None, None, 'https://www.pristinemobiledetailaz.com', 'http://frysfood.com', None, 'http://www.hotdeallio.com', 'http://locations.michaels.com/NC/GASTONIA/5006/', 'http://www.enochturnerschoolhouse.ca/', 'http://AutoNationSubaruScottsdale.com', None, None, 'https://www.mezu.ca', None, 'http://racquetclubscottsdaleranch.com', 'https://www.stbank.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://kitcarson.snappages.com/', None, 'http://manchuwok.com', 'http://affinityplumbingaz.com', 'http://www.pizzadepot.ca/locationDetails/21', 'http://www.keratinspecialist.com', None, 'http://www.sincityvapor.com/', 'https://www.thebrick.com/pages/store-mississauga', 'http://www.villasatgreenvalleyapts.com', 'http://sojoramenlasvegas.taverndesigner.site', '1592080235', None, 'http://www.timhortons.com/', 'http://www.ahappydogwash.com', None, 'http://www.lids.com', '1592080274', 'http://www.johnrobertsspa.com', 'https://northscottsdale.tapoutfitness.com', 'https://1transmission.wixsite.com', 'http://www.momdocwfw.com/mercy-gilbert', 'https://my.clevelandclinic.org/locations/directions/225-brunswick-family-health-center', 'http://charmeck.org/city/charlotte/Airport/Parking/Pages/CellPhoneLot.aspx', 'http://idealdentistryaz.com/', 'http://www.DNDC.ca', 'http://www.crescentphx.com/', None, 'http://www.regency.edu/campus/tinley-park-illinois.aspx', None, None, None, 'http://www.coffeetime.com', None, 'http://www.connectionsarizona.com', 'https://mollymaid.com/west-glendale-avondale', 'https://www.baskinrobbins.com', 'http://www.maidbrigade.com/az/phoenix', 'http://azcyclery.com/', 'https://stores.guitarcenter.com/las-vegas-lessons?source=4GOA5AJBB', 'https://rvonthego.com/arizona/paradise-rv-resort/?utm_campaign=Yelp_Directory_Listing&utm_medium=directory&utm_source=Yelp', 'http://www.ranchomanana.com/', 'http://www.stratospherehotel.com', 'http://michaeldaily.com', 'http://www.winnerstraining.com', None, 'http://monkpatisserie.ca', 'http://www.mypopcornheaven.com', 'http://www.mc3salon.com/', 'http://www.andersonentertainment.co', 'http://biggunenterprisesllc.com/', None, 'http://www.glenatmesa.com', 'https://www.hilton.com/en/hotels/msnbjhx-hampton-suites-madison-downtown/?SEO_id=YELP-HP-MSNBJHX', 'http://concordncattorney.net', 'http://www.curetondentistry.com', 'http://eastsidemarios.com', None, None, 'https://www.theflowercart.org', 'http://www.serenevegas.com', 'http://www.outback.com/locations/az/surprise', None, None, 'https://haroldstudio.com', None, 'http://alsshoerepair.com', 'https://www.garciadiamondsusa.com', None, None, 'http://bodyworkscenter.net/', 'http://www.barbershopjack.com', None, None, 'http://www.charlotterestore.org', 'http://www.chopstixhenderson.com', 'http://www.billysroadhouse.com', 'http://www.fieldclub.org/', None, 'http://www.xcitemobilegamingcharlotte.com', 'http://www.dentalhygienegroup.ca', 'https://mbveuro.com', 'http://oaksautotruckservice.com/', 'http://www.securitytitle.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/nj/colonia-2471.html?mcid=iyp:8368400', None, None, 'http://www.thecortinaapartments.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044282967372&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.gnc.com', 'http://www.nexuscarelv.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.agramgardencentre.ca', 'http://www.petvethospitals.ca/morningside-pet-hospital/', 'http://www.restomeridiana.com', None, 'http://www.face2toe.com', None, 'http://teslamotors.com', None, 'http://www.lvsmiles.com', 'http://www.starbucks.com', None, 'http://www.theweavescene.com/', None, 'http://athoriagames.com', 'http://america-sunshine-maintenance.com', 'http://www.arizonatmjpain.com', 'http://www.redrocklasvegas.com/dining/cabo.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=RR&utm_content=RR-PROPERTIES&utm_campaign=RR-YELP', 'http://www.christysnursery.com', None, 'http://www.insuranceofvegas.com/?cmpid=wj16_blm_0006', None, '1592081138', 'http://www.discount-drugmart.com', 'http://www.arrowmedaz.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://www.Rooneys.Market', 'http://www.vitalant.org', '1592081204', 'http://rsecatering.com/', 'http://rebozos.ca', 'https://www.bbbuggy.com', 'http://www.villageinnrestaurants.com', 'http://www.craigroadcarwash.com', 'http://freshsifoods.com', 'http://www.gogibson.com', 'http://www.fatburger.com/home/', 'http://www.pitapit.com/', 'http://www.aumaubree.com/', 'http://oxygenrestaurant.ca', 'https://www.freshthyme.com/store/oh-westlake/', 'http://www.tinderboxcigars.com', 'http://www.brooksidelawnservice.com', 'https://www.truecocktailsbites.com', None, 'https://www.zaxbys.com/locations/nc/denver/7179-highway-73/', 'http://www.lovethreadingbar.com/', None, 'http://truearizonaliving.com', 'http://pigandduke.com/', 'http://ignite.fortis.edu/?BID=3038&VID=SR_CID-000045038666', 'http://www.moes.com', '1592081418', 'http://www.esourceparts.ca', 'http://www.qualityinn.com/hotel-madison-wisconsin-WI089?source=pmfyelp&pmf=yelp', 'http://www.satisfiedfrog.com', None, 'http://www.fceglobal.com/', 'https://www.lifetimefitness.com/en/programs-and-events/lifestyle/lifespa/arizona/goodyear-palm-valley-lifespa-hair-skin-nail-spa-facilities.html', 'http://phoenixmoversunlimitedinc.com', 'https://curaleaf.com/stores/pl/curaleaf-az-central-85040/', 'http://www.arbys.com/', 'http://www.towcompanymesa.com', 'http://thepurrrfecttouch.com', 'https://dutchbros.com/?utm_source=las-vegas&utm_medium=yelp&utm_campaign=website_las-vegas', 'http://www.linatranstudio.com', None, 'http://www.terryalixsalon.com', 'http://www.cupcrazed.com', 'http://shymcgrath.com', 'http://asiannoodletogo.com', None, '1592084427', None, 'http://www.themandrakeclt.com', None, 'http://www.AppleOne.com', 'http://www.originalhoagieshop.com/', None, 'http://www.modernrevivalevents.com/', None, 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://calibercollision.com/locate-a-caliber-collision-center/las-vegas-downtown/', 'http://barksbubblesgrooming.com/', 'http://www.customalterationsbyanne.com', 'http://www.kingcoleducks.com', 'http://climb-cleveland.com', None, 'http://my.clevelandclinic.org/staff_directory/staff_display.aspx?doctorid=4363', 'https://www.americancampus.com/student-apartments/az/tempe/vista-del-sol', 'https://www.perfectpalmssalon.com', 'http://www.finaticsaquarium.com', 'http://www.jrsweets.ca', '1592084616', 'http://www.acuraeast.com', 'http://www.grillcity.com/nevada/bbq-grill/', None, None, 'http://www.cowlickhairsalon.com', None, None, 'http://www.magnoliaroom.com', 'https://www.wyndhamhotels.com/hotel/52962?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52962', 'http://www.pro-edgecutleryaz.com', 'http://www.elitedestinations.net', 'http://www.fourstarsushi.ca', 'http://clickserve.dartsearch.net/link/click?lid=43700006430791267&ds_s_kwgid=58700000444977937&ds_url_v=2', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.attractagency.com', 'http://www.valleyrentabox.com', 'http://Www.garbarinos.com', 'https://www.swoon.cc', None, None, 'https://www.lakenormannailsbar.com', 'http://www.studiofontana.ca', 'http://www.e-zrentacar.com/locations/las-vegas-airport', None, 'https://hpautorepair.com', None, None, 'http://www.pizzahut.com/', 'http://thesman.com/las-vegas-meadows', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://affordableweddingminister.com', 'https://www.drnnadi.com', None, None, 'https://www.autozone.com/locations/pa/wilkinsburg/208-penn-ave.html', None, None, None, None, 'https://stores.dickssportinggoods.com/nv/las-vegas/1266/', None, 'http://www.themadisonapartmentliving.com', None, None, 'http://www.entsoa.com', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.harborcrestapts.com', None, 'http://www.bottega.ca/index.php', 'https://badaxethrowing.com/axe-throwing-vaughan', 'http://www.rockincleveland.com', 'http://www.enatethiopianrestaurant.com', '1592085010', None, 'http://www.thecamptc.com', 'http://portsalonandspa.com', 'http://www.tso.ca', '1592085055', '1592085064', None, 'http://www.jimboys.com', None, None, 'http://workshopcalgary.com', None, None, None, 'http://charandarestaurante.com/', 'http://www.pattersonroofingco.com', 'http://www.armaantasteofindia.com', None, 'http://www.citywidetowing.com', 'https://www.officedepot.com/storelocator/nv/las-vegas/office-depot-3351/', 'https://www.hilton.com/en/hotels/lasethx-hampton-suites-las-vegas-airport/?SEO_id=YELP-HP-LASETHX', 'http://www.achristmasstoryhouse.com', 'http://www.cannabition.com', None, '1592085206', 'https://www.sleepcountry.ca', 'http://www.tenfeettall.ca/', 'http://myezroofsolution.com', 'http://mellomotive.com', 'http://www.sciullispizza.com', 'https://resurrectioncarpetcleaning.com', 'https://www.dodsonbros.com/location/charlotte-south/', 'http://www.russellchiro.net/', None, 'https://www.goldsgym.com/chandler-az/', 'http://fortyrodroadhouse.com', 'http://www.hendricktoyotaconcord.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, 'https://petmedic.vet/hospitals/providence-pet-hospital/', 'http://www.thewholeplate.ca', 'http://www.richardsautoclinic.com/', None, 'http://www.melonhead.ca', 'http://www.harryrosen.com/store/Vaughan%20Mills', 'http://www.rpspasta.com/', 'http://www.themaidcrusade.com', 'https://www.pintocashforgold.ca', 'http://www.willemandjools.com', 'http://www.abrazohealth.com/facilities/ArizonaHeartHospital/home.aspx', None, 'http://www.surefireinstitute.com', 'https://www.choicehotels.com/pennsylvania/coraopolis/comfort-suites-hotels/pa327/rates', 'http://www.kidszonedurham.ca', None, None, 'http://www.kennywood.com', 'http://www.avriorx.com', 'http://www.marcelwaffles.com', 'http://crumblcookies.com', 'http://www.thaiexpress.ca/', 'http://www.justincrain.com?cmpid=RV5O_BLM_0006', 'http://bestwestern.com', None, 'https://www.peoriapines.com', None, 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.aquarelarestaurant.com/Dominican_Restaurant_Toronto_-_Aquarela/Welcome.html', 'http://www.desertbloomskincare.com', 'https://locations.cibc.com/on/toronto/03902?q=Toronto%2C+ON+M4K+1P7&loc=M4K+1P7%2C+ON', 'http://masterwerks.com/', None, 'http://robertostacoshop.com', None, None, None, 'http://www.weprintvegas.com', 'https://angel-dentalcare.com', 'https://www.urbanoutfitters.com/en-ca/stores/downtown-toronto', 'https://www.repairngo.com', 'http://www.oasisislandvegas.com', 'http://www.airconditioningrepairinphoenix.com/', 'http://www.paloverdedentistry.com', 'https://www.benjerry.com/davidson', 'https://www.anytimefitness.com/gyms/690/Fitchburg-WI-53719/?utm_source=yelp&utm_medium=local', None, None, 'http://southwestcajunfest.com', 'http://locations.scootaround.com/lasvegas', 'https://www.tidedrycleanersaz.com/locations/e-frank-lloyd-wright-blvd', None, 'https://www.fragranceoutlet.com/pages/fragrance-outlet-tanger-outlets-westgate-114', 'https://www.exxon.com/en/gas-station/tempe-az-tholdings2165-321058', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.mygym.com/henderson', 'http://www.southwestbikes.com', 'http://www.thepittstopbbq.com/', 'https://www.missionmontessori.com', 'http://www.chandlerjewishpreschool.com', None, 'http://www.chinaonepgh.com', None, 'http://www.pandaexpress.com/', 'http://www.davisvilleparkvets.com', 'https://lawnlove.com/charlotte-lawn-care', None, 'http://www.stitchit.com', None, 'http://kidscuckoosnest.com', None, '1592085834', None, 'http://www.coolsummercamp.ca', 'http://www.phxskin.com/', 'http://www.magnetitecanada.com', None, None, None, None, 'http://www.diamondbackcleaners.com', None, 'http://asurology.com', 'http://www.maxstudio.com', 'http://thefloatfactor.com', 'http://www.hairdistrict.ca', 'http://www.republicservices.com/', None, 'https://order.iamaflowerchild.com', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', None, 'https://secondcup.com', None, 'http://www.altour.com', 'https://www.gogeisel.com', 'http://www.sincitytint.com', 'http://www.landeseye.com', 'http://www.superstore.ca', None, 'http://www.academyofnails.net', 'http://www.stevenkretchmer.com/', None, '1592086116', None, 'http://www.cineplex.com/Theatre/cineplex-cinemas-scarborough', 'http://www.crowbarlasvegas.com', 'http://azwindowreplacement.com', 'https://www.jrsmulchsales.com', 'http://www.mywellnessplace.com/', '1592086195', None, 'http://www.summerwindsnursery.com', 'http://palace.awardspace.com/', None, None, 'http://www.danieljsalons.com', 'http://www.southhillsortho.com', None, None, 'http://www.blackcatespressobar.com', None, 'http://jtsconcrete.com', 'http://www.magnolialanelv.com', 'http://www.bergstrommadisonchevrolet.com', 'http://www.thevillagedentalcenter.com', None, 'http://www.walterstation.beer', None, 'https://www.officedepot.com/storelocator/nc/kannapolis/officemax-6480/', 'http://www.aztacoshack.com', None, None, None, 'http://www.tranestudio.com/', 'http://www.gabroy.com', 'http://www.doughnc.com', 'http://www.maxmcqs.com/', 'http://www.popsphotoandtrophy.com', 'http://www.jaysatthelake.com', 'http://summerlinbarbershop.com/summerlinbarbershop/', 'http://www.destihl.com/', None, 'http://www.lasvegasskinspa.com/', 'http://www.northhillstoyota.com/', 'http://www.drlomboydc.com', None, None, None, None, 'https://www.hungryhowies.com/store/hungry-howies-00829?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00829&utm_content=Website_Link', None, None, None, None, 'https://www.kyrene.org/apr', 'http://www.hoopershealth.com/store-information/store-information-brampton/', 'http://www.cosmoprofbeauty.com', 'https://www.unlvmedicine.org/clinic/internal-medicine-0', 'http://www.hairyt.com', '1592086614', 'https://mettlercenter.com', 'http://stlouiswings.com', 'https://bhmanagement.com/communities/az/phoenix/cielo-apartments-1794/', 'http://woodchesterautoglass.com', 'http://castironwaffles.com', 'http://www.caronpartners.com', 'http://www.debruinchiropractic.com', 'http://proshops.bowlersmart.com/locations/nevada/bowlersmart-henderson-pro-shop-inside-strike-zone-sunset-station', None, 'http://www.windowprollc.com', 'http://www.mildreds.biz/', 'http://theupsstore.ca/45', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Phoenix/AZ/8160', 'http://www.hennaflorist.ca', 'http://murphyslaw.pub', 'http://website-3132959076228282333140-nailsalon.business.site', None, 'http://cksbbqlv.com', 'http://thewhitebrickkitchen.com/', 'http://www.teamonsiteconcrete.com', 'http://www.eighty8family.com', 'http://www.romaninconcrete.com', 'http://www.safelite.com', 'http://madison-west.certapro.com/?source=Yelp', 'http://sassygurl.ca', 'https://www.azspiritualmedium.com', 'http://yourbuybacks.com', None, None, None, None, None, None, None, 'http://www.bhfcfinancial.com', 'http://www.angelblessingslv.com/', 'http://www.stonebowlkorean.com', 'http://www.liveattheurban.com', None, '1592086982', 'http://www.bigotires.com/regions/Nevada', None, 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', None, None, None, 'http://phoenix-9thandbell.titleboxingclub.com/', 'http://www.thevineyard.ca/', 'https://www.anytimefitness.com/gyms/2195/Richmond-Hill-ON-L4E-3L6/?utm_source=yelp&utm_medium=local', 'http://www.mygreek2go.ca', 'http://stephenfolsondds.com', None, None, 'http://keyspleaselocksmith.com', None, 'https://www.woodbridgeinteriors.com', 'http://www.powernailspa.com/', 'https://www.homedepot.com/l/N-Scottsdale/AZ/Scottsdale/85260/472?cm_mmc=seo-yelp&', 'http://www.hair2000.ca', None, None, 'http://www.bestchickenwings.com/', 'http://www.faziopizza.com', 'http://www.sprint.com', None, 'http://shusalon.com/', 'https://www.lawkm.com', 'http://www.thetrteam.com/?agent=mahalalel-leli', None, 'http://5starpdrllc.com', None, None, 'http://www.bennettmedical.com', None, 'http://www.sulwer.com', 'http://www.ryerson.ca', 'https://locations.theupsstore.com/wi/fitchburg/2935-s-fish-hatchery-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.modernsalonandspa.com', 'https://scottsdaledaycare.com', 'http://www.venetian.com/casino/race-and-sports-book.html', 'http://www.waterway.com', 'https://parteeputt.com', 'http://www.vapelandphx.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.preferredpublicrelations.com', 'http://www.flashlightfactory.net', '1592087399', None, None, None, 'http://cloisterhoney.com/', 'https://horizoneye.com', 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', 'http://www.audiprestigeddo.com', None, 'http://www.hpb.com/041', 'https://stores.joann.com/nv/henderson/2015/', '1592087498', 'http://www.buldak.ca', 'https://www.westwindintegratedhealth.com', 'http://www.rtosullivans.com/', 'http://www.thechefandyou.com', 'https://locations.checkers.com/nv/north-las-vegas/2720-n.-las-vegas-blvd/?utm_source=Yelp', None, 'http://magnoliapetwc.com', None, 'http://subway.com/', 'http://gotrmc.org', 'http://www.quiktrip.com', 'http://capitalacupuncture.janeapp.com', None, 'http://www.firehousegrillingco.com', 'http://www.threesheetsdtlv.com', None, None, 'http://www.cccnevada.com/doctor/josette-e-spotts-md-facs/', 'http://www.greatclips.com/', 'http://www.kokobellibagel.com', 'http://jpsushi.ca', 'http://protechautogroup.com', None, None, None, 'http://www.teresaspizza.com/richfield', None, None, '1592087749', None, 'http://www.donsbees.com', 'http://LugariPet.com', 'http://popeyeschicken.ca', 'https://arizona-firearms.com', 'http://www.paramountbutchershop.com/', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Phoenix-AZ-85027/858046/', 'https://www.hertz.com/rentacar/location/unitedstates/northcarolina/charlotte/CLTT12', 'https://www.greendrop.com/calgary', None, None, None, 'http://www.bluelinegrille.com', 'http://www.shakeys.ca', None, 'https://www.lattaplantation.org', 'https://www.cybermax-pc-phone.repair', 'http://www.latan.com', None, None, 'http://web.archive.org/web/20071110183536/www.city.cleveland.oh.us/around_town/city_highlights/landmarks/freestamp.html', 'https://www.jerseymikes.com/3128', None, 'http://www.thecopperpalmsapartments.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.colorglolasvegas.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://www.thepotatobarn.com', 'https://northernsmokes.com', 'http://www.pandmpizzainc.com', 'http://www.brakemasters.com', 'http://www.towercitycenter.com/', 'http://www.crazymocha.com', 'http://www.bloordovercourtappliances.com', None, None, 'http://www.carmellaspizzagrill.net', 'http://www.thebluefoodtruck.com', 'http://www.kumon.com/PHOENIX-DESERT-RIDGE', 'http://www.creativeleather.com/', None, 'http://www.lecreuset.com/stores/charlotte-premium-outlets-charlotte-nc', 'http://www.ahwatukeechurch.com', 'https://stores.advanceautoparts.com/pa/carnegie/1011-washington-ave', 'https://charlotte-bjj.com', 'https://www.galleriavillage-apts.com', None, None, 'http://www.theairteamlv.com', 'http://www.northcentralsportsbar.com', None, 'https://epdpestcontrol.com', None, '1592091673', None, 'http://www.innerdivafitness.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.waltsbbq.com', 'http://www.lpoecharlotte.com', None, 'https://maps.rbcroyalbank.com/locator/searchResults.php?t=6702', None, None, None, 'https://www.campbowwow.com/cuyahoga-falls/', None, 'http://www.asba.com', 'http://cccwindowcleaning.com', 'http://metrodiner.com', 'http://www.sunnynutrition.com', None, 'https://www.jamescheese.ca', 'http://mattas.com', None, 'http://www.autoglassnow.com/phoenix', 'http://www.auntieleechampaign.com/', None, 'http://evolvedancecenter.com', 'http://www.luigismadison.com/', None, 'https://www.noodlebarphx.com', 'https://elitefloorandfurniturecleaning.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.yogibar.ca/', 'http://www.centerforbehavioralhealth.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://ineffablecaphe.com', 'http://www.thecitycafeaz.com/', 'http://www.floresfamilydental.com', 'https://www.thejoint.com/north-carolina/mint-hill/mint-hill-12029', 'http://sweetrepublic.com', 'http://www.thecaptainsboil.com?utm_source=Yelp&utm_medium=Click&utm_campaign=ON_5313Yonge&utm_content=mainlink', 'http://www.blueheel.ca/', 'http://sweetiefry.com', 'http://www.aecne.com/', 'http://www.carriepatriciastudios.com', None, 'http://www.platosclosetstrongsville.com', None, None, 'http://thegreatgreekgrill.com', None, None, 'http://www.wilderfood.ca', '1592092073', None, 'http://trunightclublasvegas.com', 'http://www.pouroliveoil.com', None, 'http://www.massagebar.com/pit.htm', 'https://penrose.edu/student-salon-and-spa', 'http://www.foodbasics.ca', 'http://www.t-mobile.com', 'http://www.azmulticare.com', None, 'http://www.yourbrowbar.com', 'https://www.advanceamerica.net', 'http://www.blossomdayspa.com', 'http://www.anticaosteria.ca/', 'http://mtholly.us/park_and_facility.php?3', None, '1592092204', 'http://www.ezpawn.com', None, 'http://wigwamcreekdental.com', None, None, 'http://enchantedcastle.info/', 'http://rosenailbarsummerlin.com', 'http://www.greatlakesbeer.com', 'http://habibizcafe.com', 'http://www.villagediscount.com/', 'http://www.tocayopgh.com', 'http://www.shuku2salon.ca', None, 'https://www.britishairways.com', None, 'http://www.elmolinocafe.com/', 'http://www.vedasfitness.com', 'https://www.infuzelv.com', None, 'http://www.winghouseandsportsbar.com/', 'http://www.eyewearatthehamptons.com', None, 'http://www.funkutzkidshairsalon.com/', '1592092400', 'http://expresssmogandmotorworks.com', None, 'https://www.affordablegaragedoor.biz', 'https://www.nhsteelecreekfamilymedicine.org', 'http://www.dhl.ca', 'http://www.azcrittergetter.com', 'http://www.smokesweinerie.com/', 'http://www.pizzapizza.ca/', 'http://www.southlandvisioncare.com', None, None, None, None, None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/1/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://iflyelite.com', 'http://www.crossfits3.com', None, 'https://www.argentaapts.com', 'http://www.guitaror.ca', 'http://hotyogaoncrowfoot.com/', 'http://Localocksmiths.com', 'https://www.tillys.com/store?StoreID=0044', 'http://www.woodbineanimal.ca', 'http://www.shilohcommunity.com', None, 'http://www.cochranvwnorth.com', None, None, 'http://www.fulloutperformance.com', 'http://caveatemptorlv.com/', '1592092620', 'http://www.bigalsbargrill.ca', 'http://www.theglostudio.com/', 'http://www.thematka.com/', 'http://thetkto.com/', 'http://www.pestcontrolguaranteed.com', None, 'http://belmontdrivein.20megsfree.com', 'http://marcellospastagrill.com/', 'http://www.roysrestaurant.com', '1592092690', 'http://aldi.us/index_ENU_HTML.htm', None, 'http://petersenicecream.com', None, None, None, None, 'https://www.hilton.com/en/hotels/phxclhw-homewood-suites-phoenix-chandler-fashion-center/?SEO_id=YELP-HW-PHXCLHW', None, 'http://www.apria.com', 'http://www.bk.com', None, 'https://www.caesars.com/caesars-palace/things-to-do/cleopatras-barge?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=CocktailCabaret&utm_content=entertainment', 'http://www.keshaschairlv.com', None, 'http://www.thesweetspotcleveland.com', None, 'http://www.3030southwater.com', 'http://www.presotea.ca', None, 'https://www.biscuitsrestaurants.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.sunscreensbymark.com', '1592092906', None, None, 'https://www.ahnenchiropractic.com', None, 'http://www.sincerelyyogurt.com', 'http://vipbilliards.ca', 'http://www.roosterscharlotte.com/', None, 'http://www.autosood.com/fr/', 'https://www.capriottis.com', 'http://www.starbucks.com/store/11135/', None, 'http://www.americanapparel.net', 'http://www.searsucker.com/scottsdale/', 'http://www.gogofresco.org', 'http://www.frankstowngardens.com/?srccode=yelp_track', None, 'https://local.fedex.com/az/scottsdale/office-2256/', 'http://www.sheahomes.com/newhomes/charlotte', 'http://www.integratedmha.com', 'http://arcadia.redemptionaz.com/', None, 'http://www.elevationoncentral.com', 'http://www.gilbertappliancestore.com', 'http://www.firelightbarn.com', None, 'http://www.southcharlotte.youvegotmaids.com', 'http://valleyprocessservice.com', None, None, None, 'http://www.foreverdiamondsjewelers.com', 'http://newmanprop.com', 'http://www.platosclosetlyndhurst.com', 'http://drappliance.business.site', 'http://99only.com/store/Las-Vegas---Beltway/', 'http://www.azbreastfedbabies.com', 'http://www.mobileaxs.ca', 'http://firstpictureframe.ca', None, None, None, 'http://advanceddermatologynevada.com/about-us/jan-fu-md-phd-faad/', None, 'http://www.sccarcenter.com', 'https://www.choicehotels.com/nevada/boulder-city/quality-inn-hotels/nv062/rates', None, 'http://www.animalkennelcare.com', 'http://www.mccandlesscrossing.com/', None, 'http://www.kmart.com/stores/pennsylvania/pittsburgh/3529.html', 'http://www.blomedry.com', 'http://www.steve-n-kids.com', 'http://www.brickandbarleyaz.com', None, 'http://www.residoor.com', None, 'http://www.massageheights.com/matthews-festival', 'https://pranaivtherapy.com', None, 'https://dillonmcdonald.vipmtginc.com/apply/', '1592093393', None, 'http://www.spamadison.com', None, None, 'http://www.drsibel.com', 'http://www.MODERNMILK.com', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', None, 'http://www.tacotimecanada.com/locations/alberta/calgary/deerfoot-meadows', 'http://www.apple.com/retail/northlakemall/', 'http://www.starbucks.com/store/10759/', 'http://www.sharkys.com', 'http://www.riggsroadvets.com/', 'http://www.head2toesmassage.com', None, 'https://www.ikea.com/us/en/stores/las-vegas/', 'http://Geeksquad.com', None, 'http://www.nevadaheadache.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.omwest.com', '1592093574', None, 'https://nolmsted.onyxhealthclub.com/contact/', None, 'http://westgatenailsspaglendale.com', 'http://www.stjosephphoenix.org', 'https://www.dickblick.com/stores/ohio/cleveland-heights/', None, 'https://www.familydentalcharlotte.com', 'http://www.swearlv.org', 'http://www.shawarmabox.ca', 'http://Www.summitpsychologicalservices.org', 'http://www.oldnavy.com/products/peoria-az-store-6364.jsp', 'http://www.myrosatis.com/store-details/Mesa%20Greenfield', 'http://www.mamarosespizza.com', None, None, 'http://www.underwrapslv.com', 'http://www.russellhendrix.com', 'http://www.wisconsinfencing.com', None, None, 'http://www.holatapasbar.com', None, 'http://www.autonationtoyotatempe.com/', 'http://www.shawarmaave.ca', None, 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, 'http://www.abcsforchildren.com', 'https://locations.sonicdrivein.com/az/tolleson/9552-west-van-buren-avenue.html', 'http://www.lackscleaning.com', 'https://www.psgdental.com/locations/precision-orthodontics-lyndhurst/', None, None, None, 'https://LimitlessGraphix.com', 'http://kachinapainting.com', None, 'http://www.fuchsiaspa.com', 'https://azfunandsun.com', '1592093870', 'http://www.deserttitle.com', None, 'http://www.trundlemanor.com', 'http://www.wrapsodygifts.com', None, 'http://tsujiri-global.com', 'http://www.sundevilbookstores.com', 'http://www.sophiespizza.ca', None, 'http://greenlifelawncare.net/', None, None, 'http://www.xoxolashes.com', 'https://www.freshcoatpainters.com/glendale-az', 'http://thesmokincue.com', None, 'http://www.centennialparkgolfcentre.com', 'https://hcpnv.com/clinic/la-canada-cardiology/', 'http://www.tanglesmadison.com', None, 'http://www.valleyartcenter.org', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.chatime.com', 'https://www.choicehotels.com/arizona/phoenix/econo-lodge-hotels/az191/rates', None, None, 'http://www.angrygorillamarketing.com', None, None, None, 'http://www.premierdentalal.com', 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', 'http://www.bunkerhillgolf.com/bar_and_grille/', 'http://advancedcleaningscottsdale.com', 'http://www.ckokickboxing.com/las-vegas.html', 'http://www.portcityclub.com/', 'https://locations.davidstea.com/on-markham-167', 'https://www.target.com/sl/streetsboro/2157', None, None, 'http://thebutlerdidit.info', 'http://www.rootcandles.com', 'http://mistertransmissionnewmarket.com', 'https://www.oxifresh.com/locations/az/paradise-valley-carpet-cleaning/?utm_source=yelp&utm_medium=social&promo_code=YP5000', 'http://www.lasvegaspropertyvaluation.com', None, 'http://www.mcknight-kitchen.com', 'http://www.aulddubliner.com/', 'http://www.cabanaondumont.com', 'http://www.lubie.ca/', 'http://www.seventattoostudio.com', None, 'http://www.goldwaterbank.com', 'http://yang39y.wix.com/xiangweixuan', '1592094322', None, '1592094333', 'https://www.johnsonlarsendental.com', 'http://www.mcadenvillemotors.net', 'https://locations.churchs.com/az-scottsdale-685', 'http://mauidogrocks.com', 'http://www.socialeatery.ca', 'http://www.newstylenailshenderson.com', 'http://eosfitness.com/location/centennial?utm_campaign=vegas-centennial&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', None, 'http://www.nicholaselectric.com', 'http://www.appetitebooks.ca/', 'http://www.futureshop.ca/', 'http://storelocator.pepboys.com/pepboys/stores/glendale/63rd_and_bell/00779', None, 'http://www.phoenix.invisiblefence.com', 'http://www.wilddogdigital.com', 'http://www.verizonwireless.com/stores/nevada/las-vegas/katie-203158/', 'https://www.davescosmicsubs.com', 'http://www.cocoshairstudio.com', 'https://www.target.com/sl/las-vegas-blue-diamond/2164', 'http://pjobrokerage.com', None, 'http://www.valleywidedoor.com', 'http://www.thaifootmassageaz.com', None, None, 'https://marketbrewingco.com', 'http://groutsmithcharlotte.com', 'http://www.bestfuneralservices.com', None, 'http://www.aactionmovers.com', 'http://www.mcsorleys.ca', None, 'http://www.camelviewpt.com', 'http://vaseklaw.com', None, 'http://www.shayacuisine.com', 'http://www.pizzapizza.ca', 'https://www.moesbarbershopaz.com', 'http://www.regencyheightsapartments.com', 'http://www.asiankitchencleveland.com', 'http://www.nationalspecialtypharmacy.com', 'https://www.spencediamonds.ca/location/vaughan-on/?utm_source=Yelp&utm_medium=Display', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://www.valleypaincenters.com', 'http://www.pipercleo.com', 'http://www.ashleysbeautylounge.com', 'http://mobiletecsmallengines.ca', 'http://www.zamrestaurant.com/', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, 'http://www.partybusesinvegas.com', 'https://www1.shoppersdrugmart.ca', 'https://www.etiquettesystems.com', None, 'http://www.hardrockhotel.com/las-vegas-restaurants/goose_island_pub', 'https://www.absolutedental.com/locations/las-vegas/2301-e-lake-mead/', 'http://uptowncheapskate.com/charlotte', 'http://www.dontortaco.com', 'http://www.spbcnc.org', 'http://www.seeingdoublecle.com', 'http://www.dogpolitan.com', 'http://www.bistrosirwilfrid.ca', 'http://crispycrust.ca', 'http://www.mcgoverns.biz', 'http://www.cadencehealthcentre.com', 'http://www.besolasvegas.com/', 'http://mayaclubaz.com', 'https://www.occphx.net', 'http://www.gamestop.com', 'http://Www.remosbistro.ca', 'https://www.petsmart.com/stores/us/az/phoenix-store0131.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.periospecs.com', None, None, 'http://www.azsingingcrepe.com/', 'http://www.andlerdental.com', 'http://bocalocaburritofactory.com', 'http://www.azbestgaragedoors.com', None, 'http://www.lazeezshawarma.com/', None, None, None, 'https://www.rightautoandtruck.com', None, 'http://www.cielostudios.ca', 'https://kirinbuffet.net', 'http://www.beatleshowvegas.com', 'http://www.metroicare.com/', None, 'https://www.bowdog.ca', None, None, 'http://www.greentreeprinting.com', 'http://www.vientianepalacerestaurant.com', 'http://jep-landscaping.com', 'http://www.germanbreadbakerylasvegas.com/', None, None, 'http://www.maxwellspine.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.greatclips.com/', '1592100552', None, None, 'http://www.drtomgreco.com', 'http://www.deerbrookefarm.com', None, None, None, 'https://americanaddictioncenters.org', 'http://www.marriott.com/cmpts', 'http://www.myspace.com/sweetsandbeats', 'https://locations.jackinthebox.com/us/az/scottsdale/20385-n-hayden-rd', 'http://www.budsayathaispalv.com', 'http://www.coderedplumbing.com', 'http://www.abcbartending.com/vegas/index.htm', 'http://www.starbucks.com', 'http://www.silversagebeef.com', None, 'http://lunchboxcafeaz.com', 'http://www.onedaypittsburgh.com', None, 'http://coolblew.com', None, None, 'http://www.oreilyauto.com', 'http://www.lvchamber.com', None, None, 'http://www.owloptometry.com', 'http://www.approvedaz.com', 'http://www.horizonlaservision.com/', None, 'http://zulmamassagetherapy.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.vapeandco.com', None, 'https://goo.gl/2UEpRZ', None, 'http://www.322PizzaBar.com', '1592100862', 'http://www.blackmountainbmx.com', None, 'http://www.dunkindonuts.com', '1592100900', None, 'http://www.crystalrivergems.com', 'http://swimmingpoolslasvegasnv.com', None, 'https://satruck.org', 'http://www.nickscalgary.com', None, None, 'http://www.caldensebakery.ca/', None, 'http://www.azsprinklerpros.com', None, None, None, 'http://www.oakridge-kennels.com', 'http://www.qdoba.com', 'http://www.arizonalodgingexperts.com/', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282947950&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.vegasconciergedoctor.com', None, 'http://www.teaspressa.com', 'http://mdrainlaw.com', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.dynastyirondoors.com', 'http://www.pineviewauto.com', 'https://www.extraspace.com/storage/facilities/us/ohio/kent/501645/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.crazymocha.com', 'https://www.royalautosales.ca', 'https://automotivediagnosticspecialties.com', 'http://www.greatescape-to.com', 'http://www.greatclips.com', None, 'https://rigatonys.com', 'http://www.sunrisemontessori.com', None, None, 'http://asavvyskincare.net', 'http://www.gabyetjules.com/', 'http://www.tcvintageaddiction.com', 'http://www.starbucks.com/store/9298/', 'http://www.CompleteLaserAZ.com', 'http://www.expressscreenprinting.com', None, None, 'http://www.tshirthell.com/', None, 'http://www.katkuphotography.com', 'http://www.greatclips.com', 'http://www.nutbrownschristmastrees.com', '1592101294', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'http://www.mrshawarmaairdrie.ca/', None, 'http://www.harborddentistry.com', 'http://porterhouseto.com/', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Pittsburgh-PA-15237/809064/', 'http://www.ihg.com/hotelindigo/hotels/us/en/scottsdale/phxin/hoteldetail', 'https://www.homedepot.ca/en/home.html?eid=LS_Google_7061', None, 'http://www.goldes.com', None, 'http://www.splitsville.ca/locations/woodbridge-bowling', '1592101389', None, 'https://www.target.com/sl/chandler-south/2747', 'http://www.worldscoutingmuseum.org', 'http://fuyaosupermarket.ca', None, 'http://www.scottsdaleaz.gov/parks/scottsdalemall', 'http://www.valleyinteriors.com', None, '1592101459', 'https://www.redradishcharlotte.com', None, 'http://www.matsudasushi.com/', None, 'http://www.starbucks.com/store/10759/', None, 'https://www.wellsfargo.com', 'http://www.stowglass.com', 'http://www.ramsey-auto.com/', 'http://mazzeolaw.com', 'https://www.tech1auto.com', '1592101541', 'https://www.suncountryheatingandcooling.com', None, 'http://www.taylorsflooringaz.com', 'http://www.asgnv.net/', 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', None, 'http://cpllabs.com/', 'http://www.dandelionretro.com/', 'http://www.freshkabob.com/', None, '1592101619', 'http://www.restorationhardware.com/', 'http://serenityspapeoria.com/', 'http://www.bannerhealth.com/locations/avondale/banner-physical-therapy-mcdowell-107th?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', None, 'http://www.phoenixcountryclub.com', 'http://www.krauterdds.com', None, 'http://sthielpilates.com', 'http://www.advanceddermatologylv.com/', 'http://www.UltraCleanExpress.com', 'http://www.littlecaesars.com', 'http://evansotg.com', 'http://www.pitabasket.com', None, 'https://www.ulta.com/stores/surprise-az-176', None, 'https://www.scaddabush.com/sherway/', 'http://www.carltonsharley.com', None, 'http://shadysidedetail.com/', 'https://www.hendersondentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://vbarbershop.com/locations/gilbert/', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85234/7110-in-gilbert/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-7110&utm_content=website-link&howheard=IYE', None, None, 'http://karsonskornbread.com', 'http://www.starwoodhotels.com/sheraton/property/dining/index.html?propertyID=205', 'http://www.pi-co.ca', 'http://www.itsbarmagic.com', None, 'http://www.painconsultantsofarizona.com', 'https://www.popeyes.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://harbour60.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.kidsacademyofcopley.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PITMC', None, 'http://www.marriott.com/hotel-restaurants/phxcb-jw-marriott-scottsdale-camelback-inn-resort-and-spa/blt-steak-scottsdale/125727/home-page.mi', 'http://www.mobilicity.ca', None, 'https://www.cricketwireless.com', 'https://www.ycsignsllc.com', 'http://www.fantasticfiredept.com/', 'http://www.busybodiesplayground.com', 'http://exquisitemobiledetailingllc.com', None, 'http://www.imperialflowershop.net/?srccode=yelp_track', 'http://www.yogaplustoronto.com', 'https://www.myessentia.ca/fr/magasins/laval/', 'https://torontovaporizer.ca', 'http://www.GurrBrothers.com', None, 'https://www.cleoms.com/meet-us/meet-the-doctor/dr-urban-picard/', None, 'http://thaipepperlv.com', 'http://www.orthoarizona.org', 'http://www.tirekingdom.com', None, None, 'http://www.barbsbridalboutique.com/', None, 'http://johnandsonsoysterhouse.com', 'http://www.allamericanlandscape.net/', None, 'http://www.kickerspizza.com', 'http://www.jlcolesalon.com/', 'http://obsessionbeautysalon.com/', 'http://www.allstateselfstorage.com/self-storage/bell-85032', 'http://www.risingphoenixllc.com', '1592102184', 'http://www.rasputinvodkabar.com', 'http://www.hkasiancuisine.com/', 'http://prioryfinepastries.com', 'http://alnolashoerepair.com', None, 'http://mvrwholesale.com/', 'http://www.rankinwomenscenter.com', 'http://www.curvyconsignments.com', 'http://www.krantzelectricinc.com/', 'http://www.gilcontool.net', 'http://www.themobilewebapps.com/repairwatchandjewelry', 'http://7eleven.ca/store-locator/33259', 'http://queencitylawn.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=2767&utm_content=bpas', None, None, None, None, 'http://www.hauntedpittsburghtours.com', 'http://www.pebooks.com/lv2/', 'http://www.kavicwinery.net/5701.html', 'http://www.waincapital.com', 'https://www.dentalsummerlin.com', 'http://slslasvegas.com/thebuffet', 'http://swensonelectric.com', None, 'http://www.westernexterminator.com/las-vegas', 'https://www.lebos.com', 'http://www.figarosbarbershop.com/', 'http://www.totallychiinc.com', 'http://www.fiddlersgreenpub.ca/', None, '1592102421', 'http://www.druglessdrs.com', 'http://www.learningrx.com/akron-bath', 'http://projectrefinedlife.com/group-private-yoga/', 'http://www.essenceairllc.com', 'http://www.amazingyoga.net', 'http://www.FatAngelosPizza.com', 'http://blinkeyewear.ca', None, 'http://www.bufords.kitchen/locations/downtown/', 'http://thenailspapgh.com/', 'http://lawanthaikitchen.com', None, 'http://harrisonautos.com', 'http://www.poppydenvegas.com/', 'http://www.reveregolf.com', 'http://clarkcountypoolandlawn.com', 'http://www.carpetsharkslv.com', 'https://www.summerlin.com/downtown-summerlin/overview.html', 'http://velvetlanecakes.com', 'http://www.cameostudio.com', 'http://1therapeuticmassage.wix.com/massage', 'http://www.muchoburrito.com', 'http://athleticmindedtraveler.com/browse-cities/toronto-on/university-of-toronto-athletic-centre', 'http://californiapools.com', None, 'http://www.apricotflowers.com', 'http://www.avon.com', None, 'http://www.MaderaPoint.com', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.mindfulwellnessaz.com', 'http://www.opalskinwax.com', 'http://www.sunkistpoolslv.com', None, 'http://www.greenroadpediatrics.net', 'http://www.room1six.com/', 'http://corktowndental.com', 'https://www.massageaddict.ca/Toronto-TheBeach', 'https://www.changingtimesdiaperco.com', 'http://www.zefiessmoothies.com', 'http://dynoplumbinglv.com', None, 'https://www.permenterchiropractic.com', 'http://scofieldrealty.com', None, None, 'https://stores.hallmark.com/nv/lasvegas/amys-hallmark-shop-lasvegas-nv-63960.html', None, 'http://www.globex2000.ca/fr', None, 'http://www.awrswheelrepair.com/pittsburgh', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Toronto-ON-M9M2R5/848075/', '1592102864', 'http://www.gnc.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.burritoboyz.ca/', 'https://ca.tokyosmoke.com/pages/queen-west', 'http://copperwillowsalon.com', 'http://www.stoughtonbuyandsell.com', 'https://integritydry.com', 'http://zero20kids.com/', None, 'http://walmart.com/', 'http://www.motel6.com', None, 'http://www.caldensebakery.ca', 'http://appliancewarehouse.com/', None, None, 'http://www.cafedejapon.com/', 'http://drshawnae.com', 'http://parrcabinet.com', 'https://www.towndentalgroup.com', 'http://www.theblindmannc.com', 'https://storelocations.ae.com/us/az/phoenix/4550-east-cactus-road.html', None, 'https://www.springspreserve.org/visitor-information/divine-cafe.html', 'http://www.solutionbuild.ca', 'http://www.northwestlimo.com', 'http://fairtradecoffeehouse.com/', 'http://www.starbucks.com/store/10759/', None, 'https://locations.wendys.com/canada/on/ajax/80-bayly-street-west', 'http://www.fredsheatandac.com/', '1592103130', 'http://newyork51pizzeria.com/', 'http://www.starbucks.com/store/14175/', 'http://www.radichisalon.com', 'https://encompasshealth.com/valleyofthesunrehab', 'http://www.fantasyautoinc.com', 'http://www.elitebusinessfilms.com', 'http://shop.pistolwhippedpastry.com', None, 'http://www.evanjstrong.com/', 'http://www.cbsquaredhairstudio.com', None, '1592103225', 'http://www.clevelandprintwear.com', None, 'http://www.jolantainteriors.com', None, None, None, None, 'http://www.pisausa.com', 'http://www.bashas.com/', 'http://www.playitagainsportscfalls.com', 'http://www.rvpaintrepair.com', 'http://www.janetkirkman.com/', 'http://www.ccvglass.com', 'https://www.massagespacharlotte.com', None, 'https://www.ritasfranchises.com/Wexford', 'http://bogartspet.com', 'https://www.jerseymikes.com/9003', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Tempe-AZ-85213/723082/', None, 'http://www.beyondconceptionmidwifery.com', 'https://www.24hourfitness.com/gyms/las-vegas-nv/rainbow-las-vegas-supersport', 'https://craftypots.studio', None, 'https://ad.doubleclick.net/ddm/clk/318369417;146857521;q?https://www.safelite.com/stores/Mesa?utm_source=yelp&utm_medium=list&utm_campaign=Addressblock&utm_content=85210_AZ', 'https://vspa-massagespa.business.site', 'https://winecollective.ca/highfield-store', 'http://www.thetoothwhisperer.com/index.html', 'https://opticas2020.business.site', None, None, 'https://drbeverlysmathisel.wixsite.com/drbeverlysmathisel', None, 'http://www.echosalonphoenix.com/index.html', 'http://www.guyspizzaco.com', None, 'http://www.dphairdesigns.com/', 'http://www.markmitsuphoenix.com', 'http://beegee-kitchen.com/', 'https://www.wm-columbuspark.com', 'http://www.infinitebeautysalon.com', None, 'http://www.sundevilauto.com/locations/az/mesa/east-mesa-power-26', 'http://www.flowersoftheworld.ca', 'http://patonthebackspa.com', 'http://pdrpizza.net', None, 'http://bankerinsulation.com', 'http://www.mainstreetcupcakes.com', None, 'http://www.veinitymd.com', 'http://mcfaddendalehardware.com', 'http://www.massagenirvana.com', 'http://www.timhortons.com', None, None, 'https://www.lush.ca/on/demandware.store/Sites-LushCA-Site/en_CA/Stores-Info?StoreID=129', 'http://www.acrepair4less.com', 'http://locations.jambajuice.com/ll/US/AZ/Scottsdale/15686-N_-Frank', 'http://www.timhortons.com/', None, 'http://www.GreaterPhoenixAreaRealEstate.com', 'http://xtremeairparks.com', 'https://www.steaknshake.com/locations/nv-las-vegas-las-vegas-boulevard-south', 'http://cambiedesign.com', 'https://ca-en.caudalie.com/boutique-caudalie-sherway-gardens-toronto', None, None, None, None, None, 'https://karachi-kabab-wala.business.site', 'http://www.azcellphones.com/', 'http://kjscurrybowl.com', None, 'https://grantmma.ca', 'http://phoenix-phx.worldairportguides.com/terminals.php', 'http://www.oldtimecandy.com', 'http://americanhomewater.com', 'http://www.footsolutions.com/summerlin', 'http://www.brownsshoes.com', None, None, 'http://eyecandispa.com', 'http://www.seanssalon.com', 'https://www.barlouie.com/locations/us/az/tempe/tempe-marketplace?utm_source=other&utm_medium=listings', 'http://www.bikramyoganphx.com/', 'http://www.nationalgolfacademy.ca', None, 'http://www.luxurymotorsports.us/used-luxury-cars-phoenix/', 'http://zcoilcf.zcoil.com/137/', None, 'http://www.fatbobpizza.com', 'http://www.swarovski.com/en-US/?utm_source=YELP&utm_medium=referral_managed&utm_campaign=YELP', 'http://www.west49.com', 'http://geigerfitness.net', 'http://Clearqualityautoglass.com', None, 'http://www.zenshinasianrestaurant.com', 'http://www.veginyyc.com', 'https://www.californiaclosets.com/locations/greater-phoenix/scottsdale-showroom/?CC5=32008&CC6=30593&utm_source=directory&utm_medium=local&utm_content=AZ166-M1-SR2', 'https://lulasewickley.com', 'http://www.fatbastardburrito.ca', 'http://www.wellsfargo.com', 'https://www.gordmans.com', 'http://www.chagrinfalls.net/', None, None, None, 'http://www.coconutclubbargrill.com', 'http://www.imaginedentistry.com', 'http://oldchicago.com/locations/champaign', 'https://www.interdent.com/gentle-dental/locations/az/mesa/1425-s-greenfield-rd-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.haysroofing.com/', 'https://www.integritycontentsservices.com', None, 'http://smilesourceonchagrin.com', 'http://etonhouse.ca', 'https://tsperformance.net', 'http://www.dressbarn.com', 'http://www.buildabear.com?sc_cid=ds:yelp:profile', 'https://locations.theupsstore.com/pa/harrisburg/4075-linglestown-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://greenwoodrentals.ca/', 'https://www.bikesourceonline.com/articles/bikesource-denver-pg502.htm', None, None, None, 'http://www.signaturehealthinc.com', 'https://www.snakesandlattes.com/location/tempe/', None, 'http://yourspacesalons.ca/tonyc', 'http://www.americanairappliance.com', None, None, 'http://www.theacvh.com', None, 'http://www.thisaint.ca', 'http://www.lasvegaswoodflooring.com/', 'https://www.insomniacookies.com/locations/store/1129', None, 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', 'http://shell.us', 'http://www.ghost-armor.com', 'http://www.thegunsmith.com/thegunsmith.html', 'http://treasureisland.com/restaurant/13/the-buffet-at-ti', None, None, 'https://www.rotorooter.com/murrysvillepa/', None, 'http://harrys-market.business.site', None, 'http://shop.hobbylobby.com', 'http://www.noodles.com/locations/south-end', None, 'https://vindalooindiancuisine.business.site', 'https://www.bowlero.com/location/bowlero-avondale?utm_campaign=webclicks&utm_medium=organic&utm_source=yelp', 'http://yardzatmirabelli.com', None, None, 'http://www.chefclaudio.com', None, None, 'http://rockfords.ca/', None, 'http://dannysdeli.net', 'http://www.foodcity.com', 'https://www.bnc.ca/particuliers/cartes-credit-mastercard/salon-aeroport-montreal.html', 'http://www.allforfun.ca', 'http://www.elyspringvalley.com', 'http://www.clubcorp.com/Clubs/Bear-s-Best-Las-Vegas/', 'http://www.dollartree.com/home.jsp', None, 'http://www.jriac.com', 'http://www.starbucks.com', 'http://www.cevw.com', 'http://realsh1ft.com', 'http://www.premiercustombuilders.com', '1592104749', 'http://www.scorelv.com/', 'http://bellaluna.us', 'http://www.jaaz.org', 'https://local.fedex.com/nc/charlotte/office-0746/', None, 'http://www.habibspersiancuisine.com', 'http://www.YouthfulDaySpa.com', None, 'http://morfinserv.com/', 'http://destinychurchlv.com', 'http://www.cabanasislandrestaurant.com', 'https://www.wyndhamhotels.com/hotel/46608?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:46608', None, 'http://downtowndetailslv.com', None, None, None, 'http://sonoranskydental.com', None, 'http://www.northcourtbeverage.net', 'http://www.restaurantdepot.com', 'http://www.hardrockhotel.com/las-vegas-restaurants/johnny-smalls', 'http://www.phoenixbimmer.com', 'https://azdonerightroofing.com', None, 'http://www.atozpediatricdentistry.com', 'https://www.titc.us', 'http://www.eastsidemarios.com/locations/ontario/toronto/scarborough/', 'https://www.assurant.com', 'http://www.westcheyennepharmacy.com', 'http://taylorhouselaw.com', 'http://kingsfamily.com/?utm_source=yelp&utm_medium=referral', None, None, None, None, None, 'http://romanticaboutique.ca', 'http://www.marriott.com/hotels/travel/cltcm-courtyard-charlotte-matthews', 'http://eagleriderhonda.com', None, '1592105051', 'http://www.hungryhollow.ca/', 'http://www.chandlercourtamc.com/', None, None, 'http://www.ultimatesportscards.com', '1592105091', 'https://www.arizonamovingcompanies.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282947950&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', None, 'https://calibercollision.com/locate-a-caliber-collision-center/charlotte-tyvola-rd', 'http://www.totalcigars.com', 'http://www.madisondancelife.com', 'http://www.pghgrille.com', 'http://www.allianceurgentcare.com', 'http://yafokitchen.com', 'http://www.abcautobodylv.com', None, 'http://www.boracaymassagevegas.com/', None, 'http://www.vetcoclinics.com', 'https://saharalasvegas.com/restaurants-bars/beers-and-bets/', 'http://www.robcoelectriclv.com', '1592105228', 'http://www.veneziabakery.com', None, 'http://www.summerspraytan.com', '1592105273', 'http://www.fresh-carpet-care.com/p/693?utm_source=bing&utm_medium=cpc&utm_campaign=EOW%20-%20Exact%20-%20Phoenix&utm_term=carpet%20cleaning', None, 'http://www.gordonwoodoptical.com', None, 'http://www.winghouseandsportsbar.com/', 'http://www.deltaco.com', 'https://www.obonsushi.com/scottsdale-quarter', 'http://www.valleyprotectiveservices.com/phoenix', 'http://www.wildgamegrillaz.com', 'http://thejewelers.com/venetian.html', 'http://www.sushiakaihana.com', 'http://www.wpahumane.com', 'http://menuderiaguanajuato.com', 'http://lambrettapizzeria.ca', 'http://www.clarkcountycourts.us', 'https://i-hvac.net', 'http://www.ichiriki.ca/', None, 'http://www.wordoflifelv.com', 'http://www.pizzaspano.ca', 'http://www.oakley.com/en/store-finder', None, None, None, 'http://overstockvehicles.com', None, 'http://hophausbrewing.com', 'http://www.pmilv.com', 'http://phoenixportablemobilewelding.com', None, None, 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=106&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-106', 'http://www.oldewinecellar.com', None, 'http://www.east4thstreet.com', None, 'http://www.synergyhomecare.com/agencies/az/sun-city/az02/', None, 'http://www.wildpurveyors.com', 'http://www.4monkeybusiness.com', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', '1592105619', None, 'http://www.starbucks.com/store/14175/', None, 'https://independenceveterinaryclinic.com', None, 'https://www.choicehotels.com/CN281?mc=blypypaf', None, 'https://opasouvlaki.ca', 'https://www.lasvegassedation.com', 'http://www.mondrianscottsdale.com/mondrian_hotel_scottsdale_redbar.asp', 'http://affordablebailbondsphoenix.com/', None, None, 'http://www.todays-market.com', None, 'http://www.jazhairstudios.com/', None, 'http://www.dwellatregency.com', None, 'http://www.skinplicitylaneese.com', None, None, 'http://www.peterpiperpizza.com/', 'http://www.BlueStateElectric.com', 'http://www.thesourcemenswear.com', 'http://pizzaandbeyond.blogspot.com/', 'https://cobblestone.com/?utm_source=yelp%C3%8A', None, 'http://www.alohausedcars.com', 'https://www.carenow.com/locations/las-vegas/eastern-horizon-ridge', None, None, None, None, None, None, None, None, 'https://www.covenantcare.com/stores/silver-hills-health-care-center/', None, 'https://www.bestwestern.com/en_US/book/hotel-rooms.66086.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:66086', 'http://avolsbookstore.com', 'http://www.mrshuizenga.com/', 'https://el-mesquite-cocina-mexicana.business.site', 'http://www.arnoldcrescentanimalhospital.com', 'http://www.valorestaurant.com', 'http://www.estheticssalonandspa.com', '1592105962', 'http://www.vape29.com', None, None, 'http://www.akronmassage.co', 'https://www.eddiev.com/', None, 'http://www.lcbo.com', None, None, 'http://www.dynamitecustomsoundsolutions.com', 'http://lacubana.ca', 'http://www.juiceandjava.ca', 'http://liftedtrucks.com', 'http://www.awildhairvegas.com/', 'https://lasvegasliving.com/properties/inspire/', 'https://www.thesteelecreekdentist.com', 'http://www.abbybelladance.com', None, 'http://www.roomstogo.com/stores/pineville/carolina-place-store/1601#utm_source=yelp&utm_medium=localsearch&utm_campaign=yelp', 'http://www.scottsdaleplaza.com/dining/jds-sports-pub-en.html', 'http://www.winners.ca', 'http://www.michaelangelos.ca', 'https://www.kohls.com/stores/pa/pittsburgh-293.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://lifedesignevents.com', 'http://www.rmcf.com', None, 'http://www.nhlakesidefamilyphysicians.org/locations--hours/prosperity-church.aspx', 'http://www.friartuckonline.com', 'http://www.getacoolbox.com', 'https://www.motel6.com/en/motels.az.phoenix.18.html', 'http://www.rockerzandrollerz.com', None, 'http://www.vegasemployment.com', None, None, 'http://kahunaville.com/', None, 'http://www.bathandbodyworks.com', None, 'http://thepinkdoorcarefree.com', 'http://www.scottsdaleaz.gov', 'http://www.midibistro.ca/', None, None, 'http://www.kingdomtitle.net', 'https://www.tdcanadatrust.com/products-services/banking/index-banking.jsp', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.liveatsanmelia.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', None, 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'https://locations.monro.com/oh/bay-village/609-dover-center-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'http://www.oakridgepizza.ca', 'http://www.myspace.com/ronnieslocal069', 'http://barbershopstyles.com', None, 'http://www.spotteddogmenu.com/', 'https://www.susanvthomaslaw.com', 'https://www.rittersdinerpittsburgh.com', None, 'http://www.rocklandtrailers.com', 'http://azcustomcoatings.com', 'https://www.bannerhealth.com/locations/peoria/banner-health-clinic-vistancia', 'http://www.bestarizonacars.com', 'http://www.kay.com', 'http://www.digitaljuiceagency.com', 'http://www.bzbarandgrill.com', '1592106459', None, None, 'http://www.aspenplumbingandrooter.com', 'http://www.allcaremedicine.com/', 'http://patriatoronto.com/', 'http://www.awomansplaceobgyn.com', None, None, 'http://www.karlsqualitybakery.com', None, None, None, '1592106550', 'https://www.popeyes.com', None, None, 'http://www.michaelangelosphotography.com', None, 'https://www.wesoothesoles.com', None, 'http://www.thechickery.com/', 'http://www.dunkindonuts.com', 'http://www.treats.com', 'https://myneighborhoodprimarycare.org', 'http://www.scottsdaleaz.gov/trolley/neighborhoodtrolley.asp', None, 'http://www.lemongrassthaicafe.net', 'https://www.bowlero.com/location/bowlero-via-linda?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'http://www.framesunlimited.com/locations/shaker-heights', None, None, None, 'http://www.nicks-automotive.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.goodwill.ab.ca/goodwill-location/varsity/', 'http://www.icaptureevents.com', 'http://www.trubuildersaz.com', 'http://www.formulakartways.com', None, 'http://chandlerdrivingschool.com', 'https://www.jacksonhewitt.com/Tax-Preparation-Services-Locations/NV/North-Las-Vegas/16008/', 'http://www.sushihousebrampton.ca', '1592106768', 'http://www.thehickorytavern.com/home/hickory_tavern-locations.php?l=Charlotte+-+Providence+Rd.', 'http://www.re-wrap.ca', None, 'http://availvapor.com', 'https://threemonksandaduck.ca', 'http://www.hihealth.com', 'http://www.starbucks.ca', 'https://www.keendogtraining.com', '1592106832', None, 'http://www.kangamooplay.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://sunrisemechanical.com/areas-served/peoria-az/', 'http://www.caminoalnorteapts.com/', 'http://www.bidwellhomeimprovement.com', 'http://www.bookbeautician.com', 'http://www.marcellos.ca', None, '1592106911', 'http://www.theroyalambassador.com', 'http://nextlevelcleaners.com/', None, 'http://www.ogdenfuneralhome.com', 'https://www.starbucks.ca', None, 'http://highlifesmokes.net', '1592106971', 'http://www.goodlifefitness.com/locations/ontario/northyork/don-millseglinton?source=yelp-websitelink-northyorkdon-gl', None, None, 'https://www.elementballantyne.com', 'http://tapeface.tv', 'http://www.hussongslasvegas.com', 'http://tidycleaners.ca', 'http://www.hksarizona.com', 'http://www.prettyininkpermanentmakeupaz.com', 'http://www.thefarmersfork.com', 'http://www.ibarbieri.com', 'http://www.barbiesgrill.com/', None, 'http://www.vegasgoldbuyers.com', None, 'http://www.anthemlandscape.com', None, 'http://www.erinssnug.com/', '1592107116', None, 'http://www.gelato64.com/?page_id=409', None, 'http://mesafamilydentistryaz.com/', 'https://locations.dennys.com/OH/ELYRIA/247158', 'https://www.closetworld.com', None, 'http://segwaylasvegas.com', None, None, 'http://getahaircutlv.com', 'http://www.ticozaz.com', 'http://www.brooksdiamonds.net', '1592107221', 'http://www.giadasitaliancucina.com', 'http://stores.barnesandnoble.com/store/2680', 'http://www.bamboobistrolasvegas.com', 'http://cestbonrestaurant.com/', '1592107261', 'http://www.euro-fine.com', None, 'https://www.wrightlawnv.com', 'http://www.booksamillion.com', None, 'http://ballersbistro.com', None, None, None, None, 'http://www.bestwaypoolservice.com', 'http://www.vfwpost7401.com/', 'http://30minutealterations.com/', 'http://www.auroranaturalmedicine.com', 'http://littlecaesars.com/', None, 'http://www.yaymaker.com', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.SecureDataRecovery.com/Charlotte', 'https://smartstopselfstorage.com/storage-locations/usa/nevada/las-vegas/smartstop-self-storage-4851-e-bonanza-rd', 'http://phoenixarc.salvationarmy.org', 'http://www.timbermesaoutdoors.com', '1592107451', 'https://www.chilis.com', 'http://www.phoenixvirtualtour.com', None, 'http://gorgeouslady.ca', 'http://www.tinderboxcigars.com', None, 'https://primpandblow.com/locations/primp-and-blow-chandler/?UTM=yelp', None, None, 'http://www.aladorpetresorts.com', 'http://www.bcbg.com', 'http://feelslikehomefarm.com/index.html', 'https://www.circlek.com/store-locator/us/ruskin/3602-hwy-41-s/2707247', None, None, None, None, None, 'http://www.kazesushi.ca', None, None, 'http://www.fabulousmanicurebar.com', 'http://www.gtatireandauto.com', 'http://www.mannyforinsurance.com/?cmpid=UGOG_BLM_0006', 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', 'http://www.torontoairportlimo-taxi.ca', 'http://Www.FlamingoCoolsVegas.com', 'http://www.secondcup.com/location/toronto-355-danforth-avenue', 'http://www.jdbyrider.com/buy-here-pay-here-pittsburg-monroeville-pennsylvania-pa114', 'http://www.djinlasvegas.com', 'http://freshco.com/stores/bloor-dundas', 'http://www.totalwine.com/store-info/arizona-phoenix-desert-ridge/1003', 'http://www.ggfarm.com/welcome-to-grateful-growers/harvest-moon-g', None, 'http://www.apassionforpetssalon.com', 'http://www.trulythaicuisine.com', 'https://www.scottsdalecfdh.com', 'https://www.legendatarrowhead.com', 'http://vehiclesunlimitedinc.com', 'http://vegasairduct.com', None, None, 'http://www.thetcmclinic.com', None, 'http://www.verizonwireless.com/stores/colorado/denver/16th-st-mall-201560/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://www.plazaloftskierland.com/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'https://www.neohioeyes.com', 'https://www.enterprise.com/en/car-rental/locations/us/az/tempe-holdeman-5015.html?mcid=iyp:8368400', 'http://www.chelseanicole.com', 'http://www.morningsidenissan.com', None, '1592139482', None, 'https://www.marriott.com/hotels/hotel-information/restaurant/yyzsb-delta-hotels-toronto-east/', '1592139508', None, 'https://www.chocolatebywickerhead.com', None, '1592139537', None, 'https://www.kneadtodestress.com', '1592139573', 'http://www.holeeburger.com/', 'http://www.gttdogs.com', None, 'https://www.faded.club', None, 'http://www.autoberry.ca', None, 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=441', 'http://www.pandaexpress.com/', 'http://www.mistyglenkennel.com', 'http://www.krispykremeaz.com', 'http://nsbank.com/', '1592139673', 'http://www.vivefitness.com/', 'http://www.mchair.com', 'http://purefitnessclubs.com/', 'http://www.bstreetrmt.com', 'http://www.rungreatrace.com/', None, 'http://lasvegas.777rentals.com', 'http://www.philipamodei.com/lasvegashairstudio/contact', 'http://www.moongsushi.com', 'http://www.capitalone.ca', '1592139757', 'https://www.discounttire.com/store/az/scottsdale/s/1284?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.cmgfi.com/agents/richard-blair', None, '1592139794', 'http://www.lvboneandjoint.com', None, 'http://www.eatgarbanzoaz.com/', None, None, None, 'https://lumenbrite.com/locations/phoenix/', 'http://www.Topspizza.ca', None, None, None, 'http://chefkennysasianvegan.com', None, 'http://www.safestoreaz.com', 'http://www.foothillsrehab.com/', 'http://www.25thstreetautomotive.com', 'https://cobblestone.com/?utm_source=yelp%C3%8A', '1592139942', None, 'https://www.bankofamerica.com', 'https://www.purebarre.com/location/westlake-avon-oh', 'http://www.tigerslairaz.com/', None, 'http://adavenkid.com/', 'http://www.shoregrillandgrotto.ca', None, 'https://www.advancedfootankle.com', 'http://www.insideoutsports.com', 'http://roysliquor.com', 'http://www.bestchoice4insurance.com', 'http://www.redkphoto.com/', 'http://www.firstchoicedental.com/locations/sun-prairie-office', None, 'https://www.target.com/sl/henderson-lake-mead-pkwy/2404', None, None, '1592140058', 'http://substationaz.com', 'http://searchthec4group.com', None, 'https://www.zimbrickaudiofmadison.com', 'http://www.mercuryautospa.com', 'http://mtclaret.org', None, 'https://www.nothingbundtcakes.com/bakery/nv/las-vegas-eastern?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=las-vegas-eastern_2', 'http://bobbyqgrill.com/', 'https://www.spring-green.com/franchise/urbana-area/', 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/etobicoke-(1).aspx', 'https://www.kohls.com/stores/az/scottsdale-620.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'https://www.abovegroundartsupplies.com/', None, '1592140190', None, 'http://www.brighterangels.com/phoenix.html', 'http://croywifi.com', 'http://www.jlbridal.com/', 'http://www.thepaperytoronto.com', 'http://brocach.com', 'http://www.balancingyourchemistry.com/', 'http://deeplyrootedhairstudio.com', None, 'http://www.chennaichettinaadpalace.com', None, None, '1592140276', 'http://gohomeplate.com', '1592140287', 'http://www.lvac.com/locations/central', 'http://www.amici-dinos.com', 'http://greenfieldjewelers.com', 'http://oldnavy.gap.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.spoonandfork.ca/spoon-and-fork-eglinton/welcome', None, 'http://fpcmesa.org', 'http://www.goodlifefitness.com', 'http://www.theecigflavourium.com', 'http://www.milagrorestaurant.com', None, 'https://www.thingsremembered.com', None, 'http://www.sambabraziliangrill.com/', None, None, 'http://fusionpowerco.com', 'http://www.michaelkors.com/', 'https://shop.lululemon.com?CID=ps_YELP_website_org', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://agents.farmers.com/az/tempe/greg-krajewski?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'https://www.sephora.com/happening/stores/pittsburgh-shadyside', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://skyvapeaz.com', 'https://pablocanada.com/shop/', 'http://www.nationalcarmart.com/', 'http://home-savings.com', 'http://chopstickexpresstogo.com', 'http://www.pathwayscounselingsvcs.com', 'http://www.petsittingscottsdale.com/', 'http://www.woodbridgevacuum.ca', 'http://www.golfwildhorse.com/', 'http://www.jennysdispensary.com', None, 'http://thericegarden.com/', None, 'https://locations.jackinthebox.com/us/nc/charlotte/7725-pineville-matthews-rd', 'https://performancetherapymassage.net', 'http://www.shinbay.com', 'http://www.solapizza.com', 'http://www.gilbertserenitydental.com/', 'http://jollyrollsicecream.com', 'http://browsbyhilary.com', None, 'http://www.adventdentistry.com/', 'http://www.mastersgalleryltd.com/', 'http://smog-king.com', None, None, None, 'http://www.a-ztennis.com', 'https://www.cellairis.com/gilbert-cell-phone-iphone-repair-yelp', 'https://made-in-argentina-la-esquina-argentina.business.site', None, 'http://www.mustardseedherbary.com', None, 'http://ivorystar.com/shows/friends-the-musical-parody', None, 'http://FoxtailLasVegas.com', 'http://www.starbucks.com/store/1006250/ca/jean-adam-st-denis/75-avenue-de-la-gare-saint-sauveur-qc-j0r-1r6/les', 'https://www.plumbcrazy4plumbing.com', 'https://www.enterprise.com/en/car-rental/locations/us/al/huntsville-madison-55ha.html?mcid=iyp:8368400', 'http://gamblerscafe.com', None, None, 'http://www.themachatgroup.com', 'http://www.mikesbarbershopmentor.com', '1592140868', None, None, 'http://chaseanddestroy.com', None, None, 'http://andersonac.com', None, 'http://www.phoenixazchinesefood.com', None, 'https://www.allnevadainsurance.com', 'https://thepolishedbrow.com', 'http://muramoto.biz', 'https://palmbeachtan.com/locations/OH/Westlake-Detroit-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=CLE', '1592140999', None, 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', None, 'http://www.campusbodysalon.com', 'http://www.lovesick.com/store-details?StoreID=9020', 'https://www.infinityfinancialmortgagecorp.com', 'http://www.atlwingsyourway.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.lvatvtours.com/', None, None, None, '1592141121', 'http://www.psychiatrylasvegas.com', 'http://www.all-starpediatrics.com', None, 'http://roomofonesown.com/', 'http://www.unityrideshop.com', 'http://villemontpizza.com/index.html', 'http://www.2bmod.com', '1592141176', 'http://washworkslaundry.com', 'https://highweedmedshop.com', 'https://mrsub.ca', 'http://gradeaid.ca', None, None, None, None, 'http://www.mrrooter.com/phoenix', None, None, None, 'https://www.sheetz.com', None, 'https://www.wyndhamhotels.com/hotel/36226?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:36226', None, 'https://www.coffeebean.com/store/usa/scottsdale/promenade-at-scottsdale', 'http://www.clearwash.ca', 'http://www.carolinavaluevillage.com', 'http://www.sincitycrossfit.com/', None, 'http://www.epennzoil.com', 'http://www.bojangles.com', 'https://www.americafirst.com/about/branches/branch-details.cfm?siteNo=233', None, 'https://www.sprint.com/storefronts/bd/sprint-south-euclid-oh-44118-fcs-1799/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://townhall.innis.utoronto.ca', 'http://www.azgreencleaning.com', 'http://pa.pittsburgh.charmingcharlie.com/fashion_accessories_pittsburgh_pa_128.html', None, 'http://www.kickaxeguitars.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YULRI', 'http://www.sunlessboutique.com/', 'https://www.dominos.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://redhousepub.co', 'http://zellaspizza.com', 'http://www.palminaleone.com', 'http://comicgirlcoffee.com', 'http://www.andreawhitten.com/', 'https://www.whitakertire.com/location/mode/1/3701-greensprings-ave-west-mifflin-pa-15122.aspx', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.taylorrentalavon.com', 'http://www.starbucks.com', None, None, 'http://www.urbanaparks.org/facilities/16.html', 'http://www.superdry.com/', '1592141552', None, 'http://hazelgeneralstore.com/', 'https://www.supercuts.com/locations/az/glendale/bell-park-shopping-center-haircuts-80215.html', 'http://www.creativetraveler.com', None, None, None, 'http://www.circabella.com', '1592141628', None, 'http://www.usps.com', 'http://www.aaronbrothers.com', 'http://www.roastmadison.com/', 'https://www.americancampus.com/student-apartments/nc/charlotte/university-crossings-charlotte', 'http://calgary.cnty.com/', 'http://locations.michaels.com/AB/CALGARY/3902/', 'http://www.home-computerhelp.com', 'http://www.thebeverleyhotel.ca', None, 'http://sachisalon.com', None, 'http://www.durafastlabel.ca', 'http://www.vegas-salon.com', None, 'http://firstchurch.church', None, 'http://www.sumitsyoga.com', 'http://www.popeyeschicken.ca', None, 'https://kneaders.com', 'https://www.turkishkebabhouse.net', None, 'http://www.subarusaintejulie.com/en/', 'http://www.eyelidsphoenix.com', 'http://www.victoriassecret.com', None, 'http://totalwellnessacupunctureaz.com/', 'http://www.maxandermas.com/locations/333038', None, 'https://www.berkshirecommunities.com/apartments/nc/charlotte/berkshire-dilworth/?utm_source=Yelp&utm_medium=Referral', 'https://www.walmart.com/store/2050/henderson-nv/whats-new', None, 'http://www.discounttirebellevue.com/', 'http://www.pizzanova.com', 'http://www.7-eleven.com/?yelp=29384', None, None, 'http://www.marriott.com/hotels/travel/yyzmk-courtyard-toronto-markham/', 'https://locations.levi.com/nv/lasvegas/denim_las-vegas_nv_188.html', 'https://www.pizzahut.ca/store-details/store-R32814/pizza-hut-Mississauga', 'http://www.onpointhairandnail.com', None, None, 'http://www.climatechnc.com', None, 'http://www.newgalleryofmodernart.com', None, 'http://www.assemblychefshall.com', 'http://www.wisconsincheesemart.com', 'http://www.gamestop.com', None, 'https://flights.hisgo.com/us/', 'http://www.starbucks.com/store/14887/', None, 'http://www.belgo.ca/', None, '1592142134', None, 'https://www.lasvegasbookkeeping.com', 'http://www.dollarama.com/', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'https://www.instantplumbing.ca', 'http://www.tintaz.com/', 'http://www.aneyefordetail.com', 'http://vanlanendds.com', 'http://www.loonspub.com/', None, '1592142216', None, '1592142226', None, 'https://www.bigfrog.com/stores/gilbert-az/', 'http://csrcoffee.com', 'http://www.expert-locksmith.ca', 'http://www.manhattanfishgrill.com', 'https://henleysfloor.com', None, 'http://www.skallywagcigars.com', 'http://www.speedandstrengthuniversity.com', 'http://www.lasvegasrestorationllc.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', None, 'http://steelecreekpediatricdentistry.com', 'http://www.mesafarmersmarketandflea.com', None, 'http://theforumatdesertharbor.com', None, 'http://addisonparkapts.com?utm_source=Local%20Listings&utm_medium=referral&utm_campaign=Top%20Line%20Local', 'http://www.greatclips.com', None, 'http://www.citi.com', None, None, None, None, None, 'http://www.7baker.ca', 'https://team-kaizen.com', None, 'https://donroyaldrycleaner.wixsite.com/website', None, 'http://www.goldstartailoring.com', None, 'http://www.planetfitness.com/gyms/charlotte-whitehall-nc-125?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.gerrysmarine.com', None, None, 'https://www.suretempair.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/oh/elyria-3931.html?mcid=iyp:8368400', 'http://www.krispykremeaz.com', 'http://www.breadandcircus.ca', None, 'https://www.millerstavernlv.com', 'http://www.marcs.com/stores/marc-s-lakewood-grocery-store-44107.aspx', 'http://www.ambrosia.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.awardscheesecakes.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FMSNCY', 'http://www.daleskarrparts.com/', 'http://www.bp.com', None, None, 'http://magictailor.ca', 'http://www.distillerypub.com/', 'http://www.deckscapes.com', 'http://www.chromasalonandboutique.com', 'https://www.bfly.ca/experience-bfly/', 'http://www.thrill-bikes.com', '1592142722', None, 'http://www.gotransit.com/publicroot/en/travelling/stations.aspx', 'http://ModManBarber.com', 'https://chocolateshops.sees.com/az/phoenix/chocolate_shops_phoenix_az_102103.html', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://sunboxphotography.biz', None, 'https://locations.monro.com/oh/painesville/1575-mentor-avenue?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', '1592142811', 'http://www.truemedispa.com/', 'http://www.realfruitbubbletea.com', 'https://az.aaa.com/agent-office-locations/az/phoenix/aaa-phoenix-office', None, 'http://jeroldoptical.com/', 'http://www.redrocklasvegas.com/dining/hachi.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=RR&utm_content=RR-PROPERTIES&utm_campaign=RR-YELP', 'http://jenniferwallens.com', None, 'https://clevelandhungarianmuseum.org', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.lakenormanchrysler.com', 'http://latitude360.com/pittsburgh-pa/', 'http://www.brewercommercialservices.com/', 'http://www.winerack.com', None, 'https://www.radisson.com/madison-hotel-wi-53719/madison', 'http://cityofhenderson.com/henderson-happenings/facilities/recreation-centers/whitney-ranch-recreation-center', None, 'http://Terminalbarbershop.com', None, 'http://www.americanapparel.net', None, 'http://www.mariospgh.com/southside/', 'http://www.shamrockroofingservices.com', 'https://www.amctheatres.com/movie-theatres/phoenix/amc-ahwatukee-24?utm_uid=yelp', None, '1592146361', 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store97', 'http://meineke.com', 'http://www.partydesignlv.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.margaritavilleglendale.com/', 'https://www.chimneystax.ca', 'http://www.palmettofamilyhearing.com', 'https://airpromaster.com', 'http://www.fresh-burger.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281380115&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://tempecomputerrepairservice.net', None, 'https://www.lvaspensalon.com', 'http://www.pacetax.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/13777+Pearl+Road-Strongsville-OH-44136/storeid=4300?cid=ps_ylp_2020', None, None, 'http://www.pandalawfirm.com', None, None, 'http://www.dominos.com', 'http://www.azuldayspa.org', None, 'http://www.koa.com/campgrounds/madison/', 'https://tinylovesphotography.com', 'https://www.imyourmechaniclv.com', 'http://www.moes.com', 'http://eng.bigbustours.com/lasvegas/home.html', 'http://www.lindleylawoffice.com', 'http://www.actiontours.com', None, 'http://www.thaizone.ca/', 'https://www.islandthymepub.com', None, None, 'https://www.efirstbank.com/customer-service/find-location.htm?loc=BELL', None, 'http://sagoautoglass.com', 'http://www.truevalue.com', 'http://www.clemcopostal.com', 'http://www.barrymorefurniture.com', 'http://www.plazahotelcasino.com/entertainment/superstars_of_magic', 'http://www.peakchiropracticpgh.com/', 'https://locations.sonicdrivein.com/nv/lasvegas/6301-w.-lake-mead-blvd..html', None, None, 'http://www.scooopskidspa.com/', 'http://www.ladybugsandwiches.com', None, 'http://www.separkmansion.com', 'https://www.ironwoodcrc.com/locations/?locations_doc=scottsdale', 'http://www.goldenlobsters.com', 'http://www.FourSonsLandscaping.net', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/north-toronto-eglington-yonge-c245.html?mcid=iyp:8368400', 'https://www.softsurroundings.com/stores/the-district-at-green-valley-ranch/', 'http://wellnesslasvegas.com', 'http://www.southernshows.com/wch', 'http://omfastfoodrestaurant.com/home.html', 'http://fuerstauto.com', 'https://www.papamurphys.com', None, None, 'http://eeleconomicrestaurantequipment.com', 'http://www.haircoloringinphoenixaz.com', None, 'http://www.oakesappliance.com', 'http://whasn.com/providers/julie-goodell', 'http://www.huntersvilleford.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.carminespizzakitchen.com', 'http://www.homedepot.ca', 'https://www.hendersonmentalwellness.com', None, 'http://onetoone.case.edu/', 'http://www.taqueriapastorcito.com', 'https://www.bakerbros.com/visitus', None, 'http://www.fallsheating.com/', None, 'http://www.starbucks.com', None, None, 'http://houlihans.com/', 'http://www.yogurtini.com', 'http://www.donvalleynorthlexus.com', 'https://www.smartstyle.com/en-us/locations/az/phoenix/located-inside-walmart-2113-haircuts-11301.html', None, 'http://www.bk.com', None, 'http://pizzabytheslice.ca/', 'http://www.shapetrain.com', 'http://coronadelsolhighschool.net/', None, None, 'http://www.wyattworks.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1015+East+Ray+Road-Chandler-AZ-85225/storeid=7849?cid=ps_ylp_2020', 'http://massageaddict.ca/oakville', 'http://Inspiradabarberandbeauty.com', 'http://www.nuvohotel.com', 'https://www.hilton.com/en/hotels/lasruru-tru-las-vegas-airport/?SEO_id=YELP-RU-LASRURU', 'http://www.starbucks.com/store/9059/', 'https://azoralsurgery.com', 'http://www.bethanyanimalhospital.com', None, 'http://www.goodeggdining.ca', 'http://www.nevadadivorce.net', None, 'http://www.classykitchenandbath.com', '1592147262', None, 'http://www.service1stenergysolutions.com/', 'http://www.vesperrx.com', '1592147301', 'http://www.chestnuthillsdental.com/locations-providers/pittsburgh-shadyside/', 'http://www.macssushi.com', 'http://www.nanashake.com', 'http://www.eyepriority.com', 'http://www.northcoastbodymod.com', None, '1592147361', 'http://www.lvcc.com', 'http://storelocator.pepboys.com/pepboys/stores/phoenix/cactus/00747', 'http://www.reginospizza.com', 'http://www.travelbughealth.com', None, None, 'http://www.mysisterscloset.com/', 'http://www.carolsconfectionspgh.com', 'http://www.altaderm.com', 'https://www.ymcacalgary.org/program-descriptions/locations/brookfield-residential-ymca-at-seton/', 'http://www.aaaonestopappliance.com', 'https://www.tonysautoshop.com', 'https://911drivingschool.com/ohio/driving-school-rocky-river-ohio/', 'http://www.gaudinporschelv.com', None, 'http://www.tuesdaymorning.com', 'http://www.tlcflooringlv.com', 'http://www.buddystubbshd.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'http://www.potterlawaz.com', 'https://www.maaco.com/locations/nc/charlotte-11619/', 'http://www.bartendingschoolc2c.com', 'http://www.millenniumsalonmadison.com', 'http://www.yak.com', 'http://rackempubandbilliards.com', 'https://restoreandrenewmassage.com', 'http://creativeillusionshairstudio.com', 'https://www.TheUltimatePartyStore.net', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.completevisioncare.com/home.html', None, '1592147593', 'https://www.northwest.com', 'http://www.arizonalullabyguild.com', 'http://www.meltwich.ca/richmondstreet/', 'http://www.aroundtheblock.com', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700006435131063&ds_s_kwgid=58700000444951711&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', '1592147657', None, None, 'http://www.littlecaesars.com/', None, 'http://cherryboomboom.com', None, None, 'http://www.azdivalashes.com', None, 'http://www.drteddysim.com/about-dr-teddy-sim/', 'http://access-handyman.webnode.com', None, 'http://www.roomforhealth.com/', 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'https://www.salt-tempe.com', 'https://nature.discoveryplace.org', 'http://www.senjivastudio.com', None, None, None, 'https://www.shijosushi.ca', None, None, 'http://www.qinthaicuisine.com', None, 'http://www.invisiblehandyman.com', None, None, 'http://headtripbrewery.com', None, None, None, 'http://www.444park.com', 'http://www.pueblomedicalimaging.com', 'http://www.the-bag-lady.biz', None, None, None, None, 'http://www.bbqisland.com', 'http://www.ohiocitynails.com', 'https://www.realstar.ca/apartments/on/brampton/188-cityview-apartments/index.aspx', None, 'http://walmart-eyedocs-lasvegas.com/Marks-Sunset', 'https://studios.waxingthecity.com/ll/US/PA/Pittsburgh/3605-Butler-Street?utm_source=yelp&utm_medium=local&utm_campaign=localmaps', None, None, 'http://omnidermatology.com', 'http://locations.in-n-out.com/234', 'http://www.eastvalleyfiduciaryservices.com', '1592148033', 'https://azflorist.com', 'https://www.meineke.com/locations/pa/pleasant-hills-2517/?utm_source=yelp&utm_medium=xvc', 'http://www.ezpoolslv.com', None, 'http://alluregardens.com/', 'http://abovethecrustpizza.com', 'http://www.alldogsgotobev.com/', '1592148088', 'http://itdotrepairs.com', None, None, 'http://www.uwhealthkids.org/locations/kidsdetail.jsp?locationId=59', None, 'http://www.visiblevoicebooks.com', 'http://www.juvenaspa.com', 'http://www.aeortho.com', 'http://www.rosestodaylasvegas.com/?srccode=yelp_track', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.charakcenter.org', None, 'http://gear-oh.com', 'http://www.wfamilydental.com', 'http://salonstylush.com/', 'http://www.westaddisonaz.com', '1592148259', 'https://www.barra-sandusky.com', None, 'http://www.denturerepairinglendaleaz.com', None, None, 'http://www.schneidersauto.com', None, 'https://datarecovery.com/about/toronto/', 'https://stores.jcpenney.com/az/phoenix/clothing-stores-phoenix-az-2889.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2889', 'http://www.picknsave.com', None, None, None, 'https://www.eliminexpest.com', 'http://www.starbucks.com/store/9298/', 'http://www.lightrx.com/mesa', 'https://local.biglots.com/pa/monroeville/1960?zcp=pd_local_yelp', None, 'http://rizzosspaghettihouse.com', 'https://www.statefarm.com/agent/US/NV/Henderson/Carl-Endorf-HYSY71YS000?cmpid=ST0N_BLM_0006', '1592148451', 'http://www.lveyedocs.com', 'https://www.usps.com/', 'http://www.fatbastardburrito.ca/locations/burrito-whitby', None, None, 'https://www.scottsdale-duilawyer.com/?utm_source=scottsdale_location&utm_medium=yelp&utm_campaign=website_link_click', 'http://arizonapianomover.com', None, 'http://www.ctrglass.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, None, None, 'http://www.rollcare.ca', 'https://locations.panerabread.com/wi/fitchburg/2960-cahill-main.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', None, 'http://www.speedlube.net', 'http://local.skechers.com/ca/glendale/38/', 'http://www.lowes.com', 'https://www.pinnaclenissan.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'https://www.ulta.com/stores/westlake-oh-1423', 'http://www.azphi.com', None, 'http://www.lacasadelahabana.com', None, None, None, 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID206', None, '1592148696', None, None, 'http://www.starbucks.com', '1592148737', 'http://www.getenzo.com', 'http://howlerspittsburgh.com', None, None, None, 'http://l.macys.com/fashion-show-in-las-vegas-nv?cm_mmc=Yelp_Stores-_-LasVegas-_-n-_-532&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Las+Vegas_532&m_ac=yelp_stores&m_ag=n', None, None, None, 'https://local.safeway.com/safeway/az/scottsdale/23565-n-scottsdale-rd.html', 'http://local.firestonecompleteautocare.com/arizona/cave-creek/4915-e-carefree-hwy/?lw_cmp=IYP_YPC_MLP_784291', 'http://www.doordoctor.ca', 'https://www.maccosmetics.com', None, 'http://www.popularpizza.ca/locations.phtml', None, None, None, None, 'http://www.craftcellars.ca', 'http://www.valleylights.com', 'http://www.quickspark.com', 'http://www.atlwings.com', None, 'http://www.OnTheSpotLV.com', None, '1592148965', 'http://www.hillsong.com/phoenix', None, None, 'http://www.divinethreading.com', 'http://www.mayfieldohdentist.com/', 'http://www.scottsdaleaz.gov/sports/aquatics/mcdowell-mountain-ranch-pool', None, 'http://www.ryah.ca/', None, 'http://www.bubblesandbowslv.com', 'http://www.houdini.com', None, None, 'http://mmgyn.com', None, 'https://www.openriceclt.com', 'http://www.mccoolspools.com', 'http://musiccentrecanada.com/', None, 'http://www.gioninos.com', 'http://www.ericpalacioslaw.com', None, 'http://www.embassygrand.com', 'http://www.firstprimerealtygroup.propertyware.com', 'http://www.sierraironlv.com', None, None, '1592149192', None, None, 'https://www.bakerbros.com/glendale', 'https://prairieflowersandgifts.com', 'https://www.sunsetgrill.ca', 'https://americanbuilderslv.com', 'https://www.petsfriend.ca', 'https://cobsdoggersandmore.wixsite.com/website', 'http://jacksaloon.com', 'http://www.thesweetpotato.ca', None, None, 'http://www.breatherefuge.com', None, 'http://www.fantasticsams.com', 'http://www.olsonortho.com', 'http://www.bulldogliquidators.com', 'http://www.ladyyorkfoods.com', 'http://storelocator.pepboys.com/pepboys/stores/las_vegas/east_charleston/00685', 'http://www.acaringnanny.com', 'http://www.markhamtheatre.ca', None, None, 'http://www.mermaidsplashnails.com', 'http://www.stephanoslv.com', None, 'https://www.peppywalnutssweetsboutique.com', None, 'http://www.courtesychrysler.com', 'http://creamistryAZ.com', 'https://www.skininjectables.com', 'http://www.lcbo.com', 'https://www.sprint.com/locations/nv/henderson/334-w-lake-mead-pkwy', None, 'http://nourishmassageandskincare.com', 'http://www.timhortons.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044280206066&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://sidelinestreeservice.com', None, 'http://www.evooristorante.com', 'http://www.budacafe.ca', 'http://leesliquorlv.com/locations/sunset-office/', None, 'https://www.jackentertainment.com/thistledown', 'http://www.orangetreepools.com', 'http://www.panorea.ca', 'http://www.cancleanpros.com', 'http://www.phxestatesales.com/', 'http://www.bareoaks.ca', 'http://www.marriott.com/hotels/travel/phxss-springhill-suites-phoenix-north/', 'http://steviespizza.com', 'http://www.7-eleven.com/?yelp=32265', 'http://tricitytowingaz.com/', 'http://www.vanillabeanonline.com', 'http://www.haggen.com', 'https://www.thebrick.com', 'http://www.appleplumbingaz.com/', 'https://www.americaroofingco.com', 'http://www.broadacresm.com', 'http://www.MobileDogWash.dog', None, None, 'http://www.cozymels.com', 'https://cacao70.com/fr/nos-emplacements/atwater', 'http://www.randstadusa.com/', None, 'http://www.soulas.ca', 'http://www.masalahousepgh.com', 'http://www.creativeformalwear.com/', None, 'http://annandalegolfclub.com/', 'http://drmikepace.com', None, None, None, 'http://www.rona.ca/', 'https://www.riosbraziliansteakhouse.com', 'http://johnnyrockets.com', None, None, 'https://www.goldencorral.com/locations/970/golden-corral-william-penn-highway', 'http://www.glendaleaz.com/parksandrecreation/ThunderbirdPaseoPark.cfm', 'https://www.daveandbusters.com/locations/pineville', '1592150792', 'http://whatisbrewing.com', None, None, 'https://www.klinkecleaners.com/locations/dane-county-locations/monroe-street', 'http://www.ymcacharlotte.org', 'http://vegasvisionoptometry.com', 'http://www.photoandgo.com', None, 'https://the-post-sports-bar.business.site', None, None, 'https://www.chevronwithtechron.com', 'https://www.audioexpress.com/locations/15115-n-hayden-road-scottsdale-az-85260/', 'http://www.kidsgardenlearningacademy.com', 'http://www.iamyoga.ca', 'http://vmacauto.com', None, None, None, 'https://www.mansion54.com', 'http://www.gogopokeus.com', 'http://www.allen-equipment.com/', 'http://tandoorigrillcalgary.com', 'http://www.indulgeculinaryacademy.com', 'http://pillartopost.com/', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=13080', None, 'http://siestalandscaping.com/index.html', 'http://storelocations.ae.com/us/pa/pittsburgh/540-south-27th-street.html', 'http://www.rockstartattoolasvegas.com', None, None, 'http://logansroadhouse.com', '1592150921', None, 'http://www.villageatcobblestonecourt.com', 'http://www.burritogordito.ca', 'http://www.tigbbqlv.com', 'http://www.fishfurniture.com', 'http://www.windowandsolarservices.com', 'http://www.pazzopittsburgh.com/', None, 'http://www.richardstreeservicellc.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://sabalimo.com', None, 'http://www.parkway-sc.com', '1592150982', 'https://www.schlotzskys.com/wisconsin/madison/1532', 'https://stores.anntaylor.com/az/scottsdale/7014-east-camelback-road.html', None, None, 'https://www.wingstop.com/location/wingstop-1394-gastonia-nc-28054/menu', None, None, 'http://www.calgarytransit.com', 'http://www.zeebasleep.com/', 'http://camdenlv.com', 'https://chicagoschickenandwafflescle.com', 'http://www.performancemarineaz.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.starbucks.com/store-locator/store/1016078', 'http://www.mullinspub.com/locations/kington-road/hours-location/', 'http://www.christensenoralsurgery.com', 'http://www.med-place.org', 'http://www.goodearthcafes.com', 'http://www.jkhlawoffice.com', None, None, 'https://prolinewindowtint.com', None, None, 'https://dainties-macaron.business.site', 'http://www.abovebeyondcleaner.com', 'https://www.petsmart.com/stores/us/oh/macedonia-store1851.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', None, None, 'http://www.heartcenterofnv.com', 'http://www.zaksbicycleshop.com', '1592151104', '1592151108', 'http://nevadaorthopedic.com/directory/people/show/thomas-vater', 'http://www.pastelesmary.com/', None, 'http://www.sciullos910.com/', 'http://www.simplyflowersnthings.com?srccode=yelp_track', 'https://www.sonoranspine.com', None, 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', None, 'https://www.wellsfargo.com', 'http://www.weymouthfarms.com', 'http://shawarmaxpress.ca', 'http://thebarrelpub.ca', 'http://www.eurekagifts.com', None, 'https://chatters.ca/stores/chatters-square-one/', None, 'http://www.lviglobal.com', 'http://hamptoncrestenc.com', 'https://www.saucepizzaandwine.com/locations/tempe-tempe-union/', None, None, 'http://tandooristyle.ca', 'http://www.associatedretinaconsultants.com', 'http://www.azeuros.com', None, None, None, 'https://www.supercuts.com/locations/az/peoria/north-valley-power-center-haircuts-82958.html', None, None, 'http://www.chassepermanentmakeup.com', 'https://www.expressoil.com/stores/gilbert/az/3502/', None, 'http://www.bestmatt.com/', None, 'http://www.nonnasplace.ca', 'http://www.commonwealthah.com', 'http://www.cigna.com/cmgaz/locations/phoenix-central-multi-specialty-center', 'http://www.safeway.com', 'http://www.roxxsouthend.com', 'http://www.torontohearingservices.com/location-contact/north-york-ontario-ca/', 'http://www.cookiedoughjo.com', 'http://www.nohiddenfeestickets.com', None, 'https://www.simon.com/mall/southpark', 'http://kintarooh.com', None, 'http://nahasushi.com/', None, 'http://www.princessauto.com', 'http://2ndandcharles.com/', 'http://www.NorterraAH.com', 'http://www.torontomenssuits.ca', 'http://www.metalmorphosis.tv', 'https://homewoodfamilyaz.org', None, 'http://www.bestpittsburghhomes.com', 'http://www.awhlawyers.com', None, None, None, None, 'http://www.rightbynaturemarket.com', 'http://www.centrooptical.com/', 'http://www.grodzinskibakery.com/', 'https://www.spoonerpt.com/locations/goodyear/', None, 'http://www.detailingknights.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.secondcup.com', None, 'http://tinyurl.com/hp44240', 'http://tokyogrill.business.site', None, 'http://www.scoopspittsburgh.com/', None, 'http://www.candlelightersnv.org/', 'http://www.grapevinewinebar.com/', 'https://www.torrid.com/store-details?StoreID=5371', 'https://freedsbakery.com/pages/freeds-dessert-shop', '1592151332', None, None, 'http://www.pandysgardencenter.com', 'http://petgrooming-charlotte.com', 'http://southlandlanes.com', None, None, None, None, 'http://www.truenorthbarbers.com', None, None, '1592151370', '1592151372', 'http://www.sunsolarsolutions.com', None, 'http://www.avenuediner.com', 'https://www.hubbardswim.com', 'http://www.canamrealestateservices.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.dreamdealers.com', None, 'http://www.rapidcollision.com', None, 'http://www.homesteadmaid.com/', 'http://www.jackinthebox.com/', 'http://www.doylechiropractic.com', 'https://dutchbros.com/?utm_source=phoenix&utm_medium=yelp&utm_campaign=website_phoenix', 'http://www.spookyfast.com/', 'http://popeyeschicken.ca/', None, 'http://huntfamilychiro.com', 'http://www.stafflink.ca/', '1592151421', None, 'https://dc-glass-glass-repair-service.business.site', 'http://www.ohiocitypizzeria.org', 'http://www.northyorksheridanmall.com', None, 'http://www.concretemadenew.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.samscyclesupply.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://graphicideals.com/', None, 'https://www.excellenceairllc.com', 'http://www.larryjsauto.com', None, 'http://www.gioninos.com', None, 'https://www.pridestaff.com/tempe', 'https://www.cinemark.com/nevada/century-orleans-18-and-xd', None, 'https://thepetclub.net', None, 'http://www.thedartshop.com/', 'https://www.greentreesportsplexpittsburgh.com', 'http://safe.frontpointsecurity.com/yelpsecurity-us', 'http://www.themagicoflearning.com/', 'http://www.westvalleyent.com/', 'http://www.lvccld.org', 'https://pizzeriamoretti.com/moretti-toronto/', 'http://www.crossfitmte.com', 'http://mcmurraych.com', 'http://murderinkproductions.com', 'http://baskonseaboard.com/', 'http://www.gracefulcakecreations.com/', 'http://www.clasensbakery.com/', 'https://jessicanailinc.wixsite.com/feelingnailsandspa', None, 'http://www.mrlube.com/en/mr-lube-near-you/Locate-a-Mr-Lube/richmond-hill-1070-major-mackenzie-drive-east.aspx?storeid=190&postalcode=L4S%201P3', 'https://www.tacobell.com/food?utm_source=yelp&utm_medium=social&utm_campaign=yelp-pilot-test-menu-static-1-CS&utm_content=paid', 'https://www.charlotteautodetailingservices.com', None, 'http://www.helzberg.com', 'http://www.haircutsarefun.com', 'http://lasvegasyardwork.com', 'http://www.innevation.com', 'https://www.cox.com/local/residential/stores/nv/henderson/545-marks-street?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q102', 'http://www.nesbitslanes.com', None, 'http://www.eggsmart.ca', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.artistictlc.com', 'http://www.wendys.com', 'https://www.haggardchiro.com/chiropractor-phoenix/', None, 'http://www.starallison.com', 'http://www.pupusaslafamiliar.com', 'http://usonv.com', 'https://www.devadave.com', 'http://www.evdi.com/?location=chandler', 'http://www.raulsoriginal.com/', 'http://www.omasplaceaz.com', 'http://www.legacynails.net', '1592151592', 'http://www.rvvh.ca/', 'https://chargrilldavidson.com', 'http://tijuanatanaz.com/', 'http://scifest.vegas/contact/', 'http://www.davinciflowershop.com', '1592151608', 'http://www.eventsbyfirstrose.com', 'http://outremont.lapiazzetta.ca', 'http://www.eurowise.com', 'http://www.rocrace.com/charlotte', '1592151621', 'https://www.wellsfargo.com', None, None, 'http://www.powerhousegym.com/schedules-i-407.html', 'http://www.dogsbycindy.com', None, 'http://www.kngmg.com', '1592151643', 'http://www.odelaybagel.com/', 'http://www.harbsbarbershop.com', None, 'http://stevedavishtgac.com', 'https://www.lajoliefemme.ca', 'http://www.alphagraphics.com/centers/westlake-ohio-us649/index.html', 'http://www.hellofacepaint.com', None, None, None, 'https://www.southwestmobility.com', None, None, None, 'http://www.lbvgallery.com', None, 'http://www.pageplusaz.com', 'http://gimelconstruction.homestead.com', 'http://www.gelatostar.com', 'https://www.lawncontrolcenter.com', 'http://www.anotherstory.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.rnrcarpetcleaning.com', 'http://www.heistbrewery.com', 'http://www.sharkystaphouse.ca/', 'https://negretelawfirm.com', None, 'http://samsxpresscarwash.com/huntersville', None, 'http://www.righttime-inc.com', None, 'https://locations.monro.com/oh/cuyahoga-falls/1584-state-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.yclibrary.org/lakewyliebranchdetails.php', 'http://www.publix.com', 'https://locations.monro.com/oh/north-olmsted/4565-great-northern-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, None, None, 'http://tonysicecream.com', 'http://bigapplebagels.com/', 'http://www.clwplumbing.com/', 'http://fcautobody.com', None, 'http://restaurants.basspro.com/FishCompany/Mesa/Default.aspx', None, 'http://www.bk.com', 'http://www.dom.pitt.edu/id/About.html', 'http://vervewellnesscenter.com/', None, 'http://www.oliveoilaz.com', None, 'http://www.nevadadentalgroup.com/', None, 'http://www.castcadearizona.com', 'http://www.JimmyJohns.com', 'http://www.generationsmedcenter.com', None, 'https://www.circlek.com/store-locator/US/phoenix/4135-w-anthem-way/2709192?location=85086', None, 'http://lotusservicesaz.com', 'http://www.mysteryadventureslasvegas.com', 'http://www.swirlyz.ca', None, '1592151813', 'http://www.kfc.ca/store/sunrige-mall-101-2525-36-st-ne-calgary', 'http://www.torontocarwrap.com/', None, 'http://www.countyofdane.com/lwrd/parks/viking.aspx', 'http://www.golfpinehills.net', 'http://www.ddsdiscounts.com', 'http://www.gailambrosius.com/', 'http://wagntails702.wix.com/vegaspetgrooming', 'http://www.rawfitnesspersonaltraining.com', None, None, 'http://www.vedatakeout.com', None, 'http://www.cocinaelvis.com', 'http://www.filosophy.ca', None, 'https://www.interstatebatteries.com/locations/all-battery-center-las-vegas-nv', 'https://www.frysfood.com/storeHours?store=66000064', None, 'http://www.kitchenova.com', 'http://www.cosmiix.com', 'http://www.7-eleven.com/?yelp=29644', 'http://www.jasonsdeli.com/restaurants/az/glendale/glendale-deli', 'http://www.clevelandtallships.com', 'http://www.eathopscotch.com', 'http://www.RentMontereyApartments.com', 'https://stores.hallmark.com/nc/matthews/jansens-hallmark-shop-matthews-nc-23514.html', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'https://www.orthocarolina.com/locations/gastonia', 'http://www.phoenixsymphony.org', 'http://balletaz.org', 'http://www.PazanGallery.com', 'http://www.teaspaceus.com', 'https://www.nsm-seating.com/national-seating-mobility-relocates-phoenix-office/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.gotyoucoveredmusic.com', 'http://handelsicecream.com', 'http://www.babessportsbar.com/', 'http://www.thegreenmango.com', 'http://teamzrestaurant.com', 'https://www.chick-fil-a.com/stapleydrive', 'http://car-detailing-cleveland.com', '1592151935', None, 'http://www.a-zequipment.com', 'http://www.adventurecjd.com', 'https://ad.doubleclick.net/ddm/clk/434423236;236814625;d', 'http://www.hotrocksdiner.com/', 'http://www.studiowe.ca', 'http://www.floorcoveringfactoryoutlet.com/', 'http://www.nutrition51.com', 'https://www.hungryhowies.com/store/hungry-howies-01809?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=1809&utm_content=Website_Link', 'http://www.zbakeryandcafe.com', None, 'http://www.payless.com', 'http://www.onefinedayphotography.com', 'http://www.sherwin-williams.com/store-locator/paint-store/Phoenix/AZ/8160', 'http://www.acehardware.com/store-details/07473', 'http://www.lacakery.ca/', 'https://agents.farmers.com/nv/las-vegas/jason-suemoto?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.scpchiropractic.com', 'http://www.housepaintinginphoenix.com', 'http://www.autoaccessoriespgh.com', None, 'http://www.baskinrobbins.com', '1592151997', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.tcby.com', 'http://www.creativestonecrafters.com', 'http://www.cocosbakery.com/', 'http://www.salonjovon.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.babyramacanada.com', None, 'https://guardlocksmithgaragedoor.com/locksmith-garage-door-repair-scottsdale-az', 'http://www.rei.com', 'https://www.burnsidebarbecue.com', 'http://www.pizzeriaviamercanti.ca/', 'https://www.sprouts.com/stores/details/-/store-details/view/store/19/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.wilsonniblett.com', 'http://www.zoltons.com', None, 'http://www.hirtsflowers.com', None, 'http://www.badboy.ca/en/pg-storelocator-Mississauga', 'http://www.blm.gov/nv/st/en/fo/lvfo/blm_programs/blm_special_areas/red_rock_nca.html', None, 'https://www.pteglv.com/locations/pts-pub/rainbow-cheyenne/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://www.crabcrackernc.com', None, 'http://magiceric.com/', 'http://www.mathnasium.com/scottsdale', None, None, None, 'http://www.textilemuseum.ca/', 'http://www.tpcmadison.com', 'http://www.freshstartaz.com', '1592152094', None, None, 'http://pizza.dominos.ca/Calgary-Alberta-10108', 'https://techfourlife.com', None, 'http://www.ttroadhouse.com', 'https://www.walgreens.com/locator/walgreens-5975+weddington+rd-matthews-nc-28104/id=10255', None, 'https://www.walgreens.com/locator/walgreens-5400+pearl+rd-parma-oh-44129/id=3314', 'http://www.ryanfootandankleclinic.com', 'http://www.hansabrewery.com', 'http://gabbys.ca/locations/gabbys-kingston-road/', 'http://westcitysnackbar.com', 'http://www.litchfield-park.org/index.aspx?NID=288', 'https://www.petsuppliesplus.com/Store/OH/Parma/Parma/120?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.centralbarkusa.com/madison-southeast', 'http://www.mattress.org', None, 'http://www.hobbylobby.com/StoreDetail/500', None, 'http://www.hairandcosaloninc.com', 'http://www.dennys.ca', 'http://bangzartandhairsalon.com/', None, None, 'http://www.joeslakewoodcomputer.com', None, 'https://milios.com', 'http://www.thescottresort.com/?utm_medium=enhanced-profile&utm_source=yelp', None, 'http://meskeremincharlotte.com/', 'http://sergio-daae.squarespace.com', '1592152184', 'http://www.courtesydental.com', None, 'http://www.soma.com/store/home.jsp?cmp=MOC_yelp', 'http://www.paradisevalleyhomes-forsale.com', 'https://thelasvegaslounge.com', 'http://www.eandgrealestate.com', 'http://www.laundrybasketvillager.com/', 'http://www.marybekitchen.com', 'http://www.gelatospot.com', 'http://professornailsandspa.com', None, 'http://www.buttermilkfinewaffles.com', 'http://www.tubeaudio.com', 'http://jeffreyngmd.com', 'http://www.lenailsonline.com', 'http://www.gnc.com', None, 'http://www.9round.com/fitness/madison-wi', 'http://www.alltattoos.net', None, 'https://www.officedepot.com/storelocator/az/glendale/officemax-6171/', '1592152244', None, 'http://www.downtownphoenixrentals.com', None, 'http://www.strawberryhedgehog.com', None, 'https://azwestpainting.com', 'http://www.abundance-a.com', 'http://silvertoncasino.com/dining', None, None, 'http://www.nellisfamilyhousing.com/', 'http://www.theloftycupcake.com', 'http://impchandler.com', None, 'http://www.lassendas.com/Casual-Family-Dining-Sports-Bar-Happy-Hour-Mesa-The-Grille-Las-Sendas.html', 'http://www.edgewaterbarandgrille.com/', 'https://www.guardianmortgageonline.com/branch-managers/arizona_mortgage_branch_manager_steve-howard/', None, None, 'http://www.marketdistrict.com/Locations/Detail.aspx?LocationID=7', None, None, None, None, None, None, 'http://ingenuitycleveland.com/', 'http://www.lcbo.com', None, 'http://www.starbucks.com', 'http://www.marcellos.ca/', 'http://www.clevelandgaragedoors.net', 'http://www.africanabbqcurriesdrinks.com', 'http://www.pvbarbers.com', 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', 'http://www.PawsPetServicesInc.com', None, 'http://svdppitt.org/stores/store-locations-directions/', 'http://www.newliferoof.com', None, None, None, 'https://agents.farmers.com/az/carefree/jason-grifo?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://venturagrill.com/', 'http://www.libertyburgers.ca', 'http://www.mushkaki.com/', None, None, 'http://www.enchantress.com', 'http://www.belfilandscaping.com', '1592152383', None, None, None, None, 'http://www.rubymarie.com', None, 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', 'http://www.dmvnv.com/', None, None, None, None, 'http://www.badattitude.com/', 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', 'http://www.ogreatcut.com', 'http://www.analoguegallery.com/', 'http://www.arizonadigestivecenter.com', 'http://www.murrysvillespa.com', 'http://www.bobstvaz.com/', None, 'https://www.rcpw.com', 'https://www.arizonatermitespecialists.com', 'http://www.familypetsalon.com', 'https://novasolutions.ca', 'https://www.kwiktrip.com/Locations/Details/673/', 'http://locations.harristeeter.com/nc/charlotte/205/', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_112', 'http://www.greenleafwholesale.com', None, 'https://nestnailwellness.com', 'http://www.lowes.com', 'http://www.soupersalad.com/', 'http://www.mammaspizza.com', 'http://www.sacredrootsaz.com', 'http://bk.com/', 'http://www.eldoradocasino.com', 'https://locations.wendys.com/united-states/wi/sun-prairie/743-w.-main-st.', 'https://salsalocamexicangrill.square.site', 'http://www.tph.ca/print/toronto-yonge-st-eglinton-ave', None, 'http://www.batteriesandgadgets.com/pages/contact_us', '1592152501', 'http://www.westthirddeli.com', 'http://www.charmeck.org/', None, 'https://growgeneration.com/?utm_source=yext', 'https://oldpinevillepremiumpub.com', None, None, None, 'http://www.swspineandsports.com', 'http://www.thepubat333.com', None, 'http://www.quiznos.com', 'http://www.autohausofnorthscottsdale.com/', 'http://www.deathinvenice.ca', 'https://sobamesa.com', 'https://wongs-chinesedining.com', None, 'http://www.megatunes.com', None, 'http://www.phoenixpaver.com', 'https://www.myplacehotels.com/my-place-hotel-north-las-vegas-nv', None, 'http://www.wehnergroup.com', 'http://liveatwynnpalms.com', None, 'http://www.artisanantiquescleveland.com', 'http://chaletvet.com', None, 'http://www.miasalonstudios.com', None, 'http://www.eatchinakitchen.com', 'http://www.williamsstainedglass.com', None, None, 'http://elcompatireshoplv.com', '1592152616', None, None, 'http://www.tbcmovers.com', 'http://www.residencesonfarmer.com/', 'https://jojosjerky.com', 'https://agents.allstate.com/mike-seifer-henderson-nv.html', 'http://www.domyresume.net', 'http://www.hongkongvintage.com/', 'http://www.newtowndds.com', 'http://www.chuparosapainting.com', 'http://ottavio.ca/contact-greenfield-park-rive-sud/', None, None, 'http://www.charmeck.org/', 'http://www.ae.com/web', 'https://www.loandepot.com/branches/Henderson-NV?sc_camp=DE925F8ECA0F4E0D8092C7E108A615A3', 'http://www.judonspainting.com', None, 'http://www.peoplesmortgage.com/loan-officer-team/broker/Tamiarmijo', None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.pinkhousenc.com/', 'http://www.kobootcamp.com', 'http://www.standa.ca', 'https://www.pepsolar.com', 'http://www.onenevada.org', 'http://623pc.com', None, None, 'http://www.expressionswaxspa.com/about-us.html', None, 'http://www.azburgershoppe.com', 'http://italianvillagepizza.com/', None, 'https://www.newportmotorslv.com', None, 'http://mandys.ca', None, 'http://www.joelcohenmd.com', '1592152774', None, 'https://www.walgreens.com/locator/walgreens-220+s+century+blvd-rantoul-il-61866/id=9965', 'http://topnotchnailsspa.com', None, 'http://www.passengerscafe.com/#hello', None, None, None, 'http://enginehouse.com', 'http://www.cartridgeworldphx.com', 'https://www.cellphonerepair.com/mayfield-heights-oh/', 'http://towingscottsdale.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.essentoronto.com/', 'http://avis.com', 'http://www.z-vw.com//?cs:pro=repman&cs:e=yelp', 'http://www.patriciacakes.com', 'http://www.acepoollv.com', None, None, 'http://www.firepatio.com', None, 'http://jerryrhynescollision.com/locations/pineville-location/', None, None, None, 'http://www.michaelkluthe.com', 'https://www.youfit.com/gym/phoenix-32nd-st-7406', 'http://www.woofgangbakery.com', 'http://www.azandersonanimalclinic.com', None, 'http://Phomono.ca', 'http://www.sunscreens-armadillo.com', None, 'http://www.donatos.com', None, 'http://www.noviamia.ca', 'http://www.paseodelpradoapts.com', None, 'http://www.redrockcanyonlv.org', 'http://Www.Tailsandbones.com', 'https://pawnscottsdale.com', None, None, 'https://www.waltsjewelers.com', None, 'http://www.oasishookahlv.com/hookahcatering.html', None, 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.ontrackdj.com', 'http://vintagelucys.com', None, 'http://www.regissalons.com/salondetail/default.asp?salonid=4818', 'http://www.DJEliteAZ.com', 'http://www.stadiumbargrill.com', 'http://kwcafeterias.biz', None, 'http://www.joycitytires.com', '1592152981', 'http://luckithaibistrolasvegas.justcafepages.site', 'http://www.thebakedbear.com', None, 'http://www.finewinereserve.com', 'http://scfapm.net/', 'http://www.shoppersdrugmart.ca', 'http://www.thrivehomeservice.com', 'http://www.atomiccomics.com', None, None, None, 'http://www.regenesisskinstudio.com/', 'https://www.searshomeservices.com/locations/appliance-repair/pa-pittsburgh/1000-robinson-center-dr', None, 'https://stores.jcpenney.com/pa/monroeville/salon-monroeville-pa-0199.html', None, 'http://www.cosmosrecords.ca', 'https://nothingbundtcakes.com/bakery/AZ/glendale?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=glendale_56', '1592153049', 'http://bentoburrito.ca/', 'http://www.bigming.ca', 'http://www.rolenbrothersfence.com', 'https://juliagrambo.com', 'http://www.automaxxon16th.com', 'http://www.flatlinegrinding.com', 'http://www.hopingfurahome.com', None, 'http://www.UrbanPranaYoga.com', 'http://www.aamfg.com', 'http://www.808smokes.com', '1592153093', 'http://restaurantlabelleprovince.com', None, None, None, 'http://www.winners.ca', 'https://www.mamabaers.com', None, None, 'http://www.risquelv.com/', None, None, None, 'https://www.KFYIadvertising.com', 'http://www.christieclinic.com', 'https://showerdoors.binswangerglass.com/nc/charlotte/?utm_source=yelp&utm_medium=social&utm_campaign=showerglass&utm_content=urllink', None, None, 'http://www.thaitouchkitchen.com/', 'http://www.bk.com', 'http://www.spinbikeshop.com', '1592153170', 'https://www.crawfordtransmission.com', 'http://www.simpleshuttle.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://www.dreamcarrentals.com/', '1592153188', 'http://www.coldstonecreamery.com', 'http://www.tonicpgh.com', 'http://www.hydroshieldphx.com', 'http://www.bk.com', 'https://wellingtonsofcalgary.com', 'https://store.vioc.com/nc/gastonia/2650-e-franklin-blvd-28052-BD0014', 'http://kimaznailspa.wix.com/kim-az-nails-and-spa', 'http://superstore.ca', 'http://www.kilkearysautobody.com', 'https://skinaddictstudio.com', None, None, None, 'http://autopricecanada.com', 'https://westvalleypawn.com', None, '1592153258', None, 'http://www.clevelandymca.org/branches/westpark', 'https://www.azcontainers.com', None, 'http://www.techspector.com', 'http://www.dunkindonuts.com', 'http://www.napoca.ca/', None, 'http://www.brownleejewelers.com', 'http://www.arbys.com', 'http://www.kearnsandco.co', None, None, 'http://www.tommulligan.com', 'http://www.vegaslimocoach.com', 'https://locations.sonicdrivein.com/nv/lasvegas/6301-w.-lake-mead-blvd..html', 'http://www.westhillvet.com/', 'http://www.mark-taylor.com/arizona/laguna/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.fourpeaks.com', None, None, 'https://www.carewithconfidence.com', 'https://elementsmassage.com/tempe', None, 'http://www.millscleaners.com', None, 'http://cluffmechanical.com', 'http://www.buenoburgeraz.com', 'https://www.cinemark.com/northern-ohio/cinemark-cuyahoga-falls-and-xd', None, 'https://www.pittsburghparks.org/schenley-park-cafe-visitor-center', 'http://www.rossocoffeeroasters.com', 'http://www.edgewalkcntower.ca/', 'http://www.dunkindonuts.com', None, '1592153386', 'http://www.shell.us/', '1592153393', 'http://www.tolmachoff-farms.com', 'https://crisp-pizza.com', 'http://www.comebuy2002.com.tw/', None, 'https://www.perfectpalmssalon.com', 'http://www.regionsbistro.com', 'http://advancedtherapeuticsmassage.com', 'http://www.davidofflv.com', 'http://www.kvegas.com', None, 'http://www.farnsworthrealty.com', 'http://blueagavemadison.com', None, None, 'https://howardair.com/showroom/', 'http://www.photographerjun.com', 'https://www.desertdryclean.com', 'http://workoutanytime.com/mint-hill', '1592153469', None, None, 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', 'http://www.merlenormanstudio.com/nv/las-vegas/mn-10293/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.divasalonspa.com/', None, 'http://www.alexandani.com/pittsburgh', 'http://www.antoniospizza.net', '1592153499', None, None, 'http://www.pittsburghsbestremodeling.com', 'https://cvam.com', None, None, None, 'http://www.magomindfulness.org', 'http://www.twolouiesmarket.com/', 'http://www.runningroom.com/hm/', 'http://www.gamestop.com', 'http://www.fabletics.com', 'http://captiverooms.com', None, 'http://ad.doubleclick.net/clk;266326037;92222803;c?http://www.24hourfitness.com/FindClubDetail.do?clubid=205&edit=null&semiPromoCode=null&cm_mmc=Yelp-_-ClubPage-_-BusinessListing-_-Link', None, 'http://www.7-eleven.com/?yelp=19726', '1592153554', None, 'https://www.kalonsandglidewell.com', 'https://roiproperties.com', 'https://www.truenorthmortgage.ca/?utm_source=Yelp&utm_medium=yelp-ads&utm_campaign=yelp-ont', None, 'http://www.scottsdaleautogroup.com', None, None, 'http://www.papamurphys.com', '1592153591', 'http://www.beneficial-insurance.com', None, 'http://katespade.com', 'http://www.purelifehomeopathy.com', 'https://www.nhrandolphobgyn.org/locations--hours/charlotte.aspx', None, None, 'http://www.olgaallenhairsalon.com', 'http://www.cabowabocantina.com/vegas/', 'https://apricotlaneboutique.com/store/champaign/', 'https://locations.noodles.com/wi/fitchburg/2981-triverton-pike-dr--at-mckee-rd.html', 'http://clickserve.dartsearch.net/link/click?lid=43700044282974602&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.tlchudson.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://www.gmgbarbershop.com', 'https://communitytirepros.com/tires-auto-repair-6-phoenix-az', 'http://www.calgary.ca/CSPS/Recreation/Pages/Athletic-parks/Glenmore-Athletic-Park.aspx', None, 'http://www.2dadsbouncehouses.com', 'http://www.INTLscottsdale.com/', 'http://www.xingfutang.ca', 'http://www.thelashandsugarcompany.com', None, 'https://stores.hallmark.com/nc/pineville/amys-hallmark-shop-pineville-nc-38803.html', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEAA', None, 'https://www.azmonsterair.com', 'http://knockout-fitness.com/locations/gilbert/', None, None, None, None, None, None, '1592153709', None, '1592153714', 'https://vercini.com/stores/vercini-miracle-mile-shops-las-vegas/', 'http://signaturegalleries.com/ACs_Wyland_Signature.html', None, None, None, 'http://marsiglianospizzeria.com', 'http://www.byashleymarie.com', 'http://www.dominos.com', None, None, None, 'https://www.americasbest.com/store-list/pineville-la-71360/', None, None, 'http://www.kbbicycleshop.com', 'http://mastertune.ca', None, None, 'http://www.stevesknows.com', 'http://www.shopplanetblue.com', 'http://www.89002realtor.com', 'http://www.peoplesutility.com', 'http://www.silverstatecu.com', 'http://www.crossfitmagna.com', 'https://www.olivegarden.com/locations/ab/calgary/calgary-northgate-plaza/4345?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:calgary-ab-4345_pl:locurl_rd:1743', 'http://dishosteria.com', 'http://gcbc.gcu.edu', None, 'http://www.bluewaterimaging.ca/', 'https://bikedepot.com/stores/toronto/', 'http://angelosgilbertbarbershop.com', 'http://www.teacoffee.com', 'https://locations.usbank.com/index/arizona/phoenix/west-bell-rd-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.nevadacoinmart.com', 'http://www.cupcakes-canada.ca', 'http://www.mastertoddy.com/', 'http://www.venetian.com/restaurants/italian/tintoretto-restaurant-bakery.html', None, 'http://www.videoproductionscottsdale.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXEL', 'http://www.wineandspiritfestival.ca', 'https://www.supercuts.com/locations/ca/oakland/rockridge-district-haircuts-8050.html', 'http://www.cvlt.org', 'http://www.9round.com/fitness/madison-wi', 'http://hobakkoreanbbq.com', 'https://beavertails.com/shops/', 'http://friendsofdormontpool.org/pool.html', 'http://www.applyapprovedauto.com', None, 'http://www.customdentures.us', 'http://www.partysavvy.com', 'http://www.oliverannie.com', 'http://abrazodiabetes.com', 'http://www.i9sports.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.dunkindonuts.com', 'http://www.crossfitcholla.com', 'http://HairMajesty.mysalononline.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://vespucciconsignment.com', 'http://www.dominos.com', 'http://www.hangoverbail.com', 'http://www.harmonybarandgrill.com', 'http://LiveAtArtessa.com', '1592153958', 'http://drkaylaeckart.com', None, 'https://www.va.gov', 'http://www.starbucks.com/store/9334/', 'http://thesweatlab.com', None, None, None, 'http://www.homesense.ca', None, 'http://www.dominos.com', None, 'http://www.zerorezpgh.com', None, None, 'http://whasn.com/locations/whasn-henderson/', '1592154010', 'https://haircutmenraintreeranchchandleraz.com', 'http://themonticello.com', 'http://www.seagullbook.com/', None, 'https://www.publicstorage.com/arizona/self-storage-mesa-az/85210-self-storage/787?pid=wyelp&CID=1245&CHID=AFL', 'http://protecrepair.biz/', 'https://www.vapeloft.com/vaughan-vape-shop', 'http://www.futons-4-less.com/', 'http://www.unitedcabcle.com', 'http://www.pinkladiesmaids.com/', None, None, 'http://www.heroburgers.com', 'http://www.coinlesslaundry.com', 'http://www.mortgageandcreditpro.com', None, None, 'http://www.caesarspalace.com', 'https://www.gohealthuc.com/north-carolina/charlotte/quail-hollow?utm_source=yelp&utm_medium=referral&utm_campaign=yelp%7Clistings%7C2020-nc-null-novant-011520-quail-hollow', None, '1592154093', None, 'http://www.akanails.com', None, 'http://doorfiftyfive.com/', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'http://northamericanspine.com/', 'http://www.nutrishopcharlotte.com/', None, 'http://www.plazaappliancemart.com', None, None, 'http://www.chickrotisseriebar.com', None, 'http://www.losolivosrestaurants.com', None, None, None, 'www.rustycage.ca', None, 'http://www.newcityphx.com/', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.pnponecarecleaning.net/', 'http://ronsserviceandtire.com', 'https://simonmed.com', 'http://www.streetsaw.com', '1592154185', '1592154189', 'https://bosshairsalon.com', '1592154198', 'http://www.speedydetail.ca', 'http://www.dentalspalv.com', None, 'http://www.taketimetorelax.com', None, 'http://www.lvcmc.com', 'http://www.fkaiser.com', None, 'http://www.vinorossorestaurant.com', None, 'http://www.dwellstudentmadison505.com', None, 'http://www.DornHardware.com', None, 'https://www.atmosphere.ca/stores/calgary.html', 'http://anvilbaraz.com', 'http://thetreeguylv.com', None, 'http://www.redrockcanyonlv.org', 'http://www.chachis.ca', 'http://www.decadenceculinary.com', None, 'https://www.sierracanyonaz.com', '1592154281', 'https://providenceeye.com', 'https://locations.sonicdrivein.com/il/savoy/101-calvin-street.html', 'https://cosmomusic.ca', '1592154349', 'http://www.banfield.com/veterinarians/az/phoenix/pho?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.desertspringsrealty.com', 'https://www.valuecityfurniture.com/store-locator/pa/pittsburgh/451-clairton-blvd', 'https://www.speedy.com/shops/newmarket/en/', 'https://stores.anntaylor.com/factory/us/nv/las-vegas/7400-las-vegas-blvd-south.html', 'http://splashwindowcleaning.com', None, 'http://incascuisine.com', 'http://kierlanddentalcenter.com/', 'http://www.cherrystbbq.com', 'http://www.hznvet.com/', 'https://www.enterprise.com/en/car-rental/locations/us/oh/chardon-3928.html?mcid=iyp:8368400', 'http://www.gansercompany.com', 'http://casaritasmexicangrill.com', None, 'https://www.theelementlv.com', 'http://www.olde8automotive.com', 'https://www.241pizza.com', 'http://kindmedsaz.com', None, None, 'http://www.blimpcitybikeandhike.com', None, None, 'http://www.championfenceinc.com', None, 'https://www.anytimefitness.com/gyms/3397/Montreal-QC-H2W-1Y7/?utm_source=yelp&utm_medium=local', '1592154453', 'http://www.enchantedvalleyacres.com/', 'http://furbabiesresort.com', None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', 'http://www.visualcreations.vegas', 'http://www.phoenixazhomes4u.com/', '1592154476', '1592154480', 'http://www.phoenixmedicalgroup.com', 'http://www.azvpcp.com', 'https://www.petsmart.com/stores/us/nv/las-vegas-store1153.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://www.sellitquickhs.com', 'http://a1carpetmasters.com/', None, 'http://www.arcoflifechiro.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, 'http://www.sears.com/stores/north-carolina/monroe/0002008.html', 'http://www.EliteBartend.com', 'http://www.adriaticflooring.com', 'http://www.BombHairVegas.com', 'https://www.sonoraquest.com/find-a-location/sun-lakes-alma-school-riggs/', None, 'https://www.bluebreeze216.com', 'http://www.swgeneral.com', 'http://www.wetpetsandfriends.com', 'http://www.dirkcpa.com', 'http://www.alivedanceworks.com', 'http://www.coldstonecreamery.com/stores/20181?latitude=33.6071829&longitude=-111.9403254', 'http://www.silhouettebridallv.com', 'http://www.alibabas.ca/index.php?route=common%2Flocation_details&loc_id=12', 'http://www.jakesbarvegas.com/', None, 'http://www.sav-onplumbing.com?srccode=yelp_track', None, 'http://www.edelmanplumbing.com', 'http://www.starbucks.com/store/11823/', 'http://www.scentair.com', None, 'https://www.ihop.com/en/restaurants-south-las-vegas-nv/7490-s-las-vegas-blvd-3096', None, 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/mississauga-(2).aspx', 'http://www.aspirekidsports.com', 'http://www.bloodbrothersbrewing.com', 'http://www.sherwin-williams.com/store-locator/paint-store/Gilbert/AZ/8286', 'http://www.blackeagletoronto.com/', 'http://www.maderacabinets.com', 'http://www.citycleaner.com', 'http://todaysinteriors.com/', 'http://4seasonslandscapinglv.com', None, None, 'http://ashleynailsspachandler.com', None, 'https://www.walmart.com/store/1646/mesa-az/details', 'http://www.daphnesbakery.com', 'http://www.vynepowdercoating.com/', '1592154609', 'http://www.cityfresh.org', None, None, 'http://www.crystalsatcitycenter.com', None, None, 'http://www.accountingprose.com/accountingprose-arizona/', 'https://order.pizzapatron.com/menu/phoenix-indian-school-road?utm_source=Yelp&utm_medium=Order&utm_campaign=Ordering', None, 'http://www.beachesbrewing.com', 'http://www.robertocarpetclean.com', 'http://skyharbor.com', 'http://www.brodywebdesign.com', None, '1592154648', None, None, 'http://www.puckettsfarm.com', 'http://www.bishopsplum.com', 'http://www.alleen.com', 'https://www.hilton.com/en/hotels/clemehx-hampton-suites-cleveland-mentor/?SEO_id=YELP-HP-CLEMEHX', 'http://www.ariatroofing.com/', 'http://yazlounge.com', 'http://www.safaripetcenter.com', 'http://www.sukhothaibistro.com/', 'http://teavana.com/ca', 'http://www.furniturestopaz.com/', 'http://www.apexoutdoortreeservices.com', 'http://meridianlv.com', None, None, 'http://www.eddys.com', 'http://www.bobscopyshop1.com', '1592154699', 'http://www.kingspointsmallengine.ca', 'http://www.elpolloloco.com/locations/store/5541', 'http://www.skinstudioaz.com/', None, None, 'http://www.liquordepot.ca/?utm_source=Yelp&utm_medium=Online_Listings&utm_content=Location&utm_campaign=LiquorDepot_AB_Q3_July_September_2017', 'http://www.hcdentallv.com', 'http://www.tomduffyinsurance.com', None, 'https://www.chandleraz.gov/explore/chandler-aquatics/centers-and-pools/folley-pool', 'https://jessieleephotos.com', 'http://Www.crawlingsquidtattoo.com', 'http://www.bojangles.com', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.airportlimocanada.com', '1592154747', 'http://www.wellsfargohistory.com/museums/phoenix', None, 'https://www.xtremevapour.com', '1592154760', 'http://sunvalleynailspa.com/', 'http://www.quantumcollections.com', None, None, 'http://www.grandstayhospitality.com/find-a-hotel/locations/mount-horeb/overview', 'http://www.swingpt.com', 'https://certapro.com/summerlin/?utm_source=YextNetwork&utm_medium=organic&utm_campaign=YextNetwork', None, 'http://biggscamera.com', 'http://www.deekerssidetracks.com/', 'http://www.humblewinebar.com', 'http://www.theofficepub.ca', 'http://hhtattoo.com', 'http://www.blackphoto.com', None, 'http://kakaallyoucaneat.com', 'http://www.restartbar.com', None, None, 'http://kiplinautorepair.com/', 'http://www.thepizzacompany.biz', 'http://www.checkeredmoon.com', '1592154823', 'http://www.michaelpwebbersondds.com', None, 'http://www.potbelly.com/MayfieldHeights', 'https://www.walgreens.com/locator/walgreens-2363+s+lindsay+rd-gilbert-az-85295/id=5215', '1592154837', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://www.kirchappliance.com/', 'https://www.erinparktoyota.com', 'http://www.parkatdeervalley.com', 'http://www.westgateaz.com', 'http://www.sugo.ca', None, 'http://bellacinos.com', None, 'http://mintstrength.com', 'http://www.napolivince.ca', 'https://parsleymediterranean.com', 'http://sweeteezsweets.com', 'http://www.pspohio.com/', 'http://www.readytuxedo.com', 'http://www.wildchildclothes.com', 'http://www.mexicanbowl.ca', 'https://bostonpizza.com/en/locations/sunridge.html', None, 'https://www1.shoppersdrugmart.ca', 'http://www.baskinrobbins.com', None, 'https://www.long-mcquade.com/location/Ontario/Brampton', '1592154901', 'http://www.uhhospitals.org/westlake/urgent-care', 'http://www.wholehomeinspectionsllc.com', 'http://www.beautif-eyestudios.com', None, 'http://allbritematerials.com', 'http://www.victoriassecret.com', 'http://www.fransrestaurant.com', 'http://www.fandoctor.com', 'https://www.popeyes.com/store-locator/store/restaurant_83325', 'https://www.usstoragecenters.com/self-storage/arizona/glendale/us-storage-centers/126', 'https://stores.nordstromrack.com/us/az/gilbert/2090-e-williams-field-road?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=154&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', 'http://www.trilogylife.com/communities/arizona/vistancia/', 'http://www.carmellaspizza.com/', 'http://www.skysongcenter.com', 'http://www.sessomsandsons.com', 'http://fossilandhaggis.com/', None, None, 'http://casablancanails.com', None, 'http://www.erbertandgerberts.com/locations/detail/sun-prairie', 'https://cafevialinda.com', 'http://www.tesororanchapts.com', 'http://www.icecreampizzaworks.com', 'http://www.pizzanova.com', 'http://www.te-koop.ca', None, 'http://www.cardealsdirect.ca', 'http://getnutslab.com', 'http://www.artinthepark.org/', None, None, None, 'http://www.CampanasPizza.com', None, None, 'http://www.phoenix.gov', 'http://www.pwaesthetics.com', None, 'https://www.encantopoolcare.com', None, None, 'http://greekstop.ca', 'http://www.mortproductions.com', 'http://trendsettereyewear.com', 'http://www.starbucks.com/store/15887/', None, 'https://www.anytimefitness.com/gyms/4028/Mint-Hill-NC-28227/?utm_source=yelp&utm_medium=local', 'https://www.gowireless.com/stores/az/goodyear/goodyear-estrella-marketplace/', 'http://www.kitchenstuffplus.com', None, 'https://www.choicehotels.com/CN283?mc=blypypaf', 'http://phxfloors.com', 'http://www.tenpennyimc.com', 'http://www.winchellspub.com/', None, None, 'http://www.kisellasurgery.com', 'http://www.thegraniteshopofmadison.com', 'http://www.coffeebean.com', 'http://www.completeeyecareaz.com/', 'http://www.palazzo.com/azure', 'http://www.azinspector.com/', 'http://www.dollartree.com/home.jsp', None, 'http://www.cartersgymnastics.org/', None, 'https://www.extraburger.ca', 'http://www.elhefe.com/scottsdale', 'http://www.baschs.com', None, 'http://www.monroevillekia.com', 'http://farmersfurniture.com/', None, None, 'http://www.abestautorepair.com', 'http://www.northlakechiro.com', 'http://drkennedychiro.com/', 'http://www.artgalleryofmississauga.com/index.html', 'http://www.uptowncharlottecleaner.com', 'http://www.buckdeitzphotography.com', 'http://www.manuelsaz.com/', 'http://www.funkymunky.ca', 'http://tandmautomotive-hub.com', 'http://smokespoutinerie.com', 'http://www.galleriashoppingcentre.ca', 'http://www.functionpilates.com', None, '1592155146', 'http://www.allthingseyeslv.com', None, None, None, 'https://www.mgmgrand.com/en/nightlife.html', 'https://arizona.weidner.com/apartments/az/phoenix/arezzo/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.flawlessfaceandfigure.com/', '1592155164', 'http://www.clerkofcourt.maricopa.gov/', 'http://www.chaska.ca/', 'http://www.highdesertoralsurgery.com', 'http://www.wins.doitbest.com', 'http://www.gtmassages.com', 'https://www.pioneerfamilypools.ca/locations/newmarket/', None, 'https://www.lvspaandnailsvegas.com', 'http://thebikeproject.org', 'http://www.850Degrees.ca', 'https://stores.joann.com/oh/hudson/171/', None, 'http://www.phoenixlockoutsandroadsideassistance.com', 'http://www.bettercontracting.ca', 'https://www.popeyes.com', None, None, 'http://icirides.com/', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.ritascleaningllc.com', None, '1592155224', 'http://www.rockbottom.com/', 'https://soswaxlv.com', None, 'http://www.pelicanssnoballs.com/lakewylie123.php', 'http://www.shopmetcalfes.com', None, None, 'https://www.themotherhoodco.com', None, 'https://losgirasoles.us', None, 'http://www.bowlofgreensfinesalads.com', None, 'http://planetpetopia.com', 'http://www.platinumentourage.com', 'http://www.drsteed.com', None, 'http://www.chopchopwok.com/', 'http://www.mizumisushi.ca', None, 'http://www.lachotsmiles.com', 'http://www.laketowne.com', 'http://www.carolynes.com', 'http://www.golfsmith.com', 'http://www.themerchant.biz', None, 'https://thepetclub.com', 'https://www.loszarapes.com', 'http://www.dmvnv.com/locat.htm', 'http://www.mrpuffs.com/fr/', None, 'http://distilledbeautybar.com', 'http://www.intothefirepizza.com', 'http://www.womeninneed.net/', 'http://www.rianahairstudio.com', 'http://planetsmoothie.com/', 'http://www.asianhealingartsandacupuncture.com/', 'http://www.sosappliancerepair.com', 'http://www.greaterlasvegasdental.com', None, None, 'https://www.cellphonerepair.com/phoenix-central-az/', 'http://GreenMaid.Info', 'http://www.goldennugget.com/home/entertainment_attractions/defending_the_caveman/', 'http://www.vegasvacuumsewing.com', None, 'http://www.rockwoodnaturalmedicine.com/', 'http://www.club42.com', 'http://newmarket.colmustardspub.com', 'http://www.lazyloafandkettle.com', None, None, 'http://www.thepilatesbodylasvegas.com', None, None, None, 'http://www.laptopxchange.com/phoenix-az-computer-repair/', 'https://www.4pawspetresort.com/?utm_source=yelp&utm_medium=social', 'https://www.cartridgeworld.com/las-vegas-nv/89102-0318/about-us', None, None, 'http://www.economy-glass.com', 'http://www.novaristorante.ca', None, None, 'http://locations.harristeeter.com/nc/davidson/268/', 'https://dentalsolutionslv.com', 'http://www.doggiedoorsontherun.com/', 'http://www.thaicuisineexperts.com', 'http://www.aztechglasstint.com', None, None, 'http://www.designercakeshop.com', 'http://www.myfoodcity.com', 'http://www.kmart.com/stores/michigan/monroe/4098.html', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'https://www.themetatfashioncenter.com/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.mcqueenplumbing.com/index.html', None, 'http://communityculinary.org/', 'http://www.classroomcentral.org', None, 'http://www.saltydogpetspa.net', 'http://www.thebodyrx.com', None, 'https://www.moonvalleynurseries.com/services/tree-service?utm_campaign=yelp&utm_source=yelp-az&utm_medium=tree-care', 'http://www.wm.com/', '1592155455', 'https://dema.az.gov/army-national-guard/papago-park/arizona-military-museum', 'http://www.glendalesalonaz.com', 'http://www.hcpnv.com/clinic/wynn', 'http://www.noirtraining.com', 'http://www.heritagecrownaz.com', 'http://massageworkscharlotte.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=803&utm_content=bpas', 'http://www.OrganicMassageCleveland.com', 'http://www.BeefOBradys.com', '1592155482', 'http://www.parktowerapts.com', 'http://chartiersanimalhospital.com/', 'http://ordercasadeplata.com', 'https://www.omniwellnesscenter.com', None, None, 'http://www.horsinaround.ca/', 'https://petvalu.com/location/2034', None, None, 'http://www.karlaskarslv.com/', 'http://www.dogsuppliesvegas.com', 'http://www.savon.com', 'http://www.foodbasics.ca', 'http://www.cryscakecreations.com/', 'https://www.autorepairpittsburghpa.com', 'https://vrplayin.ca', None, 'http://www.philsebastian.com', 'http://www.gvdentalcenter.com/', 'http://www.barringtonplaceapts.com/', 'https://locations.theupsstore.com/az/surprise/15508-w-bell-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.hinkleyslighting.com', 'http://laptopexpert.com', 'http://www.bathandbodyworks.com', 'http://www.jimmysnycpizzeria.com', 'https://locations.theupsstore.com/az/phoenix/4802-e-ray-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.rotaryevolution.net/', None, None, 'http://www.baskinrobbins.com', 'http://www.apple.com/fashionshow', 'http://www.gohunanofstow.com', None, 'http://www.piacere.ca', None, 'http://www.azcenturypoolplastering.com', 'http://www.acclivityhealthcare.com', None, None, 'http://www.gallaghersexpertautorepair.com', 'http://www.containerbaryyc.com', None, None, 'https://www.superstitiongrandantiquemall.com', None, None, 'https://beehiveceilings.com', 'http://www.toppackgear.com', None, 'https://www.medexpress.com/location/pa/pleasant-hills/plp/?utm_source=yelp&utm_medium=paidsocial&utm_campaign=Evergreen', None, None, None, 'http://www.phoenixgreyhoundpark.com', None, '1592155627', 'http://www.autobell.com', 'http://slshotels.com/lasvegas/', None, None, 'https://www.hilton.com/en/hotels/pitsmes-embassy-suites-pittsburgh-downtown/?SEO_id=YELP-ES-PITSMES', 'http://bestchinainc.com', None, '1592155648', None, 'http://www.ArrowAH.com', None, 'http://dswcenter.com', None, '1592155660', None, 'https://tonyspokerschool.com', 'http://www.aetna.com', 'http://www.pizzafire.com', 'http://www.cakesonthemove.com', 'http://www.mandeljcc.org/', 'http://www.shakesandfranks.com', 'http://www.erindaleanimalclinic.com/', None, 'http://www.bloorwestvet.com', None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/501/?utm_source=yelp&utm_medium=listing&utm_campaign=website', None, 'http://www.bestmatt.com/', 'https://agents.allstate.com/wes-cain-gilbert-az1.html', None, 'http://www.scoutandcash.com', None, 'https://soccerpostarrowhead.com', 'http://www.saeedsbarandgrill.com', None, None, 'http://www.thesuntanboutique.com', None, None, 'http://www.childrensurgentcare.com', None, 'http://www.nikospizzalasvegas.com', None, None, 'https://enjoi-nails-salon.business.site', None, None, 'http://poolpartsplus.net/', None, None, 'https://locations.davidstea.com/on-toronto-1', 'http://clickserve.dartsearch.net/link/click?lid=43700006435127445&ds_s_kwgid=58700000444950505&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://myamericanfurnituregalleries.com', 'https://www.circlek.com/store-locator/us/peoria/9476-w-olive-ave/2706468', 'http://www.tikiicevegas.com', None, None, '1592155772', 'https://www.challengerschool.com/campus/nevada/las-vegas/silverado', None, 'http://www.fredmeyerjewelers.com', 'https://shadysidehousecleaning.com', None, 'http://serranosaz.com', 'http://www.expressflooring.com', None, 'http://www.clarkcountynv.gov/depts/clerk/services/pages/civilmarriages.aspx', 'http://griegofamilyeyecare.com', None, 'http://www.thunderbirdobgyn.com', 'http://www.bowkerchiropractic.com/', 'https://www.ventospizzapgh.com', 'http://www.minhchauoptical.com', None, 'http://www.michael-a-anderson.com', 'http://www.thewallpapermarketofmesa.com/', 'https://www.lvac.com/locations/henderson', 'http://subway.com/', 'http://www.sarphx.com', 'http://rokvegasnightclub.com', None, 'http://www.dovespa.ca', 'http://www.reprodux.com/', None, 'http://www.birch-dan.ca', 'http://www.nellosauto.com/', 'https://fantasticworldscomics.com', None, 'https://arizonadental.com/contact/phoenix-az-office/', None, 'http://www.strongsvillevacuum.net', 'http://www.ufixitautomotive.com', 'http://www.greenlinehair.com', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85255/787-near-pinnacle-peak/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-787&utm_content=website-link&howheard=IYE', 'http://www.fremontweddingchapel.com', 'http://eh25.com/tasting-room/', 'http://www.paramountfinefoods.com', None, 'http://www.stevenjosephphotography.com/reviews', 'http://www.trappedcle.com', None, 'http://roxannesonline.com/', None, 'https://www.medusacle.com', None, None, 'http://www.fikesnet.com', 'http://cobraplumbing.net', 'http://www.tranteam.com', 'http://chinaaaadelivery.com', 'http://www.gangnamstreetlv.com', None, None, None, None, None, None, 'http://www.rapidrehablv.com/', '1592155928', 'https://reviveptandwellness.com', 'http://www.bronzebeautyst.com/', 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'http://www.dunkindonuts.com', 'http://www.savers.com', 'http://www.kulinars.net', None, None, 'https://www.tesla.com/findus/location/store/calgary', 'http://www.vibebeautylounge.com', None, 'http://www.sunsetstation.com/entertainment', '1592155959', 'https://www.moneytreeinc.com/branch/north-nellis', 'http://refinedlandscaping.com/', 'http://www.enterprise.com', 'http://www.kidsrkidsmatthews.com', None, None, 'http://www.simsroofingandsiding.com', 'http://www.shoplostfound.com/', 'http://www.galaxylg.com', 'https://www.chopsticksngrill.com', None, None, 'http://www.cal-am.com/communities/tropicana-palms', 'http://www.johnsfamilyrestaurant.com', 'https://www.toronto.ca/data/parks/prd/facilities/complex/337/index.html', 'http://www.onehazelton.com/', 'http://www.handinhandpreschool.com/index.html', 'https://diminishedvaluecheck.com', None, 'http://www.BradyLuxury.com', None, 'http://www.bikramyogamesa.com', 'http://www.niceguystechnology.com', '1592156015', None, 'https://www.kohls.com/stores/oh/macedonia-235.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.castlemegastore.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=phoenix_yelp&utm_content=2017', None, 'http://www.kingwongchinese.com', 'http://l.macys.com/scottsdale-az?cm_mmc=Yelp_Stores-_-Scottsdale-_-n-_-450&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Scottsdale_450&m_ac=yelp_stores&m_ag=n', 'http://www.therisingsun.ca/', 'https://www.ahn.org/locations/healthwellness-pavilion/peters-township', None, 'https://www.impactarcherylv.com', None, None, None, 'http://www.greatclips.com/', None, None, 'https://www.rossoutdoors.com', 'http://www.allianceurgentcare.com', None, None, None, 'https://bounceu.com/matthews-nc', 'http://www.thestudiosalon.biz/', 'http://www.jackieo.ca', None, 'http://www.owlremodeling.com', 'http://wiglewhiskey.com', None, None, None, 'https://store.vioc.com/nc/denver/7575-highway-73-28037-GM0004', None, 'http://www.mymindseyerecords.com', None, None, None, None, 'https://www.themovingmasters.com', 'http://www.rodgunandbarbers.com', 'https://locations.davidstea.com/on-toronto-1', 'http://scottsdaleautoglass.com', None, 'http://ad.doubleclick.net/ddm/clk/283420830;110240480;l', None, 'http://prestigebeautysalo.wix.com/prestigesalon', 'https://www.tileshop.com/store-locator/north+charlotte.do', 'http://www.colkerjanitorial.com/', 'http://www.justforpleasurenc.com/just-for-pleasure-2-north-charlotte-nc/', None, 'https://www.accucaredental.com', 'http://www.eltororestaurante.com', 'https://www.dicksspeedotach.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://trunzosauto.com', 'https://www.originaljoes.ca', '1592156149', 'http://RalphieMayVegas.com', None, 'http://www.greengrotto.ca', None, 'http://carolinashomestone.com', 'https://www.montecarloinns.com/markham-suites', 'https://www.wellsfargo.com', 'https://www.marathonpetroleum.com', 'http://www.recordsreduction.com', 'https://www.rmcf.com/AZ/Tempe50423', '1592156173', None, 'http://www.newcenturyhairdesign.com', 'http://www.bloorwestwinery.com', 'http://www.costco.com/warehouse-locations/scottsdale-az-427.html', 'http://thearomatherapygarden.com', 'http://www.aaronlending.com', 'https://local.biglots.com/nv/las-vegas/4500?zcp=pd_local_yelp', '1592156193', None, 'http://nes-electrical-services.business.site', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2faz%2fphoenix%2fmesa-west&sisearchengine=1524&siproduct=BEMES_Bus', 'http://othermamalv.com', 'http://www.n15salon.com', 'http://www.eastmesapediatrics.com/Home_Page.php', 'http://www.timhortons.com', 'http://www.shoelessjoes.ca', 'http://www.85254.com', 'http://www.funasiancuisine.com', None, 'http://mazzagarden.com/', 'http://www.littlecaesars.com/Locations/tabid/92/location/28079/Default.aspx?id=MTU1MzAwMTc%3d', 'http://www.accesstohealthcare.org', 'https://www.kidsquest.com/location/redrock/', 'http://www.siegelandcompany.com', 'http://www.miraclesofphoenixfitness.com', None, 'https://www.sheetz.com', 'http://www.elysianatstrose.com/', 'http://Www.federalgalley.org/restaurants/Shaka/', 'http://www.bowiechiropractic.com', 'https://www.topnotchwrapslv.com', 'http://simplicitysalonlv.com/', 'http://www.resumesolutions.ca', 'http://www.steamwayservices.com', None, None, 'https://collegehunkshaulingjunk.com?utm_source=yelp&utm_medium=organic', 'https://www.italianrestaurantrivergate.com', 'https://www.booksamillion.com', 'http://www.starskycanada.com/aboutus.php?s=4', 'http://www.platinumwellness.net', None, None, None, 'http://www.sheratoncavaliercalgary.com/calgary-restaurant', 'http://www.massagealacarter.com/', 'http://www.vintagewireandsupply.com', 'http://www.meyersmanagement.com', 'https://www.orthoarizona.org/physicians/Caleb-Behrend', 'https://heartlandfarmsanctuary.org', 'http://benefitcosmetics.com', 'http://stores.sportsauthority.com/az/phoenix/sporting-goods-phoenix-692.html', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd', 'http://www.thespiritconnection.com', None, 'http://Adventurehelicoptertours.com', None, 'http://www.studiowish.com', 'http://www.luckybrand.com', 'http://www.glamorgananimalclinic.com', 'http://evermorenevermore.com', 'http://www.flooring2day.com', 'http://www.rosedrivingschool.com', None, 'https://www.marquiscompanies.com/facility/marquis-centennial-hills/', 'https://www.queenofheartscasinoparties.com', 'https://store.vioc.com/wi/stoughton/1108-us-51-138-53589-GR0034', 'http://solylunabeautystudio.com', None, 'http://chinatocleveland.com', 'http://www.coffeedaklak.com', 'https://www.ediblearrangements.com/fruit-arrangements?utm_campaign=StoreID561&utm_medium=Listing&utm_source=Yelp', 'http://www.christophier.com', 'http://www.paramountfinefoods.com', None, 'http://www.ballantynevillage.com', 'https://stores.advanceautoparts.com/nc/charlotte/2910-freedom-drive?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', 'https://www.walgreens.com/locator/walgreens-6649+morrison+blvd-charlotte-nc-28211/id=1376', 'http://andysmechanicalser.mechanicnet.com', None, 'http://www.mattressfirm.com/', None, None, 'https://www.sandmanhotels.ca/hotels/calgary-airport/', 'http://www.MontysFurniture.com', 'http://www.urbanamarket.org', 'https://roadside-picnic.business.site', 'https://www.woolfeyecare.net', 'http://www.neatedupey.com', 'http://www.azpluscleaning.com', 'http://www.JimmyJohns.com', None, 'http://www.doubletreeinspectionsofaz.com', None, None, 'http://www.habitburger.com', None, 'http://www.ShaolinArizona.com', 'http://www.providencecourtapts.net', None, 'http://howardstowingpittsburgh.com/', 'http://www.fantasticsams.com/', None, None, 'http://www.contessacatering.com', 'http://projectmanagementacademy.net/las-vegas/pmp-certification.php', 'http://www.scottsdalelibrary.org/', 'http://richtreenaturalmarket.com/', 'http://www.heightslibrary.org/', 'http://www.alibabas.ca/index.php?route=common%2Flocation_details&loc_id=1', 'http://www.lids.com', 'http://www.terracharlotte.com', 'http://l.macys.com/chandler-az?cm_mmc=Yelp_Stores-_-Chandler-_-n-_-453&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Chandler_453&m_ac=yelp_stores&m_ag=n', 'http://www.galleriaatsunset.com', None, 'http://www.primrosegilbertsantan.com?utm_campaign=localmaps&utm_medium=maplistings&utm_source=yelp', 'http://www.glendalebarber.com', 'http://www.costnerlaw.com', 'http://www.permanentbeautyusa.com', 'http://www.scottsdaleaz.gov/Parks/chap.asp', 'http://www.picknsave.com', None, 'http://freshandeasy.com', None, None, 'https://www.teslamotors.com/en_GB/findus/location/store/rosspark', 'http://bmwofchampaign.com', 'https://pvpd.com', 'http://www.poisonivysalon.com.', 'http://www.rmfenceohio.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://motherstamales.com', 'http://www.pamier-kabob.com/', None, None, None, 'http://www.mabelsbakery.ca/', 'https://www.hilton.com/en/hotels/clepwht-home2-suites-cleveland-independence/?SEO_id=YELP-HT-CLEPWHT', 'http://www.costco.com/warehouse-locations/henderson-nv-673.html', 'http://www.smiledesigncenterlv.com', 'http://www.mononachinastar.com/', None, 'https://www.trendssalonllc.com', 'http://www.heysugarstudio.com', 'https://www.choicehotels.com/arizona/scottsdale/rodeway-inn-hotels/az437/rates', 'http://www.thorespressobar.com', None, 'https://izzysbakeryandcafe.com', 'http://tonydblc.webs.com/', None, 'https://www.teamlogicit.com/PhoenixAZ302/', '1592156578', 'http://clickserve.dartsearch.net/link/click?lid=43700006430431858&ds_s_kwgid=58700000444952719&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', '1592156585', None, 'https://www.palmetto-eye.com', 'http://www.solaireonscottsdale.com/', 'http://www.westernreservehospital.org', 'https://www.sleepcountry.ca', 'http://theupsstore.ca/148', 'http://www.vip-pools.com', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89084/600-in-north-las-vegas/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-600&utm_content=website-link&howheard=IYE', None, 'http://7eleven.ca/store-locator/33259', 'https://www.popeyescanada.com/maps/toronto-liberty-village.html', 'http://www.theproducebox.com', 'http://www.elitepestcontrolnv.com', 'https://www.worldwidegolfshops.com/locations/van-s-golf-shops-mesa-801-s--power-road.html', None, 'http://www.wearejoviec.com', 'http://www.zajecpainting.com', 'http://www.spicy-garden.ca/', 'http://www.pittsburghoralsurgery.com', 'https://www.alterationsandcreationsaz.com', 'http://www.marriott.com/hotels/travel/yyzfs-fairfield-inn-and-suites-toronto-airport', 'http://www.wetseal.com', None, 'http://www.gioninos.com', None, None, 'http://www.gioiabeautybarspa.com', 'http://homedetectiveohio.com/', 'http://www.4seasonstreesllc.com', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.buylaptops.ca/', 'http://www.pittsburgh.va.gov', 'https://hoame.ca/contact-us/', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', None, 'http://eatzencore.ca', None, None, None, None, None, 'http://www.teamfreemanhomeloans.com', None, '1592156716', None, 'http://www.snapfitness.com/fountainhills', None, 'http://www.scooterscoffee.com', None, 'http://www.szechuanexpress.com/', 'http://baycoins.wordpress.com/', 'http://www.computerlasvegas.com', None, None, 'http://familylawguys.com/contact/scottsdale', 'https://www.sephora.com/happening/stores/phoenix-jcpenney-at-ahwatukee-foothills', '1592156756', None, 'http://www.swanpizza.com', 'http://cartridgeworldphx.com', 'http://www.amerizonaproducts.com', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.bridlewoodmall.ca/', None, 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=clein&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', None, 'http://www.faithculture.ca', '1592156791', 'http://www.itsugar.com', 'https://local.fedex.com/az/phoenix/office-5048/', '1592156801', 'http://www.monkeybargym.com', None, None, None, None, 'http://www.quiktrip.com/', 'http://www.signaturewellness.org/', 'http://junipergrill.com', 'http://www.michaudscatering.com', 'http://www.bikeandforth.ca', 'https://www.artlewinbespoke.com', None, 'http://azteamania.com', 'http://www.miegakoreanbbqcleveland.com', None, 'http://goldenasiancuisine.com/', 'http://southparkvet.net/', 'http://www.tamcapturesphotography.com', 'http://www.glotique.com/', 'https://www.t-mobile.com/store-locator/az/chandler/chandler-fashion-center?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://asapcity.com', 'https://www.idealimage.com/medspa-locations/nevada/las-vegas-nv-area/lasvegashendersongreenvalley', 'http://Www.ktsfish-chicken.com', 'http://dreamdinners.com/main.php?page=store&id=53', 'http://www.rockstarhotdogs.com/', None, 'http://www.scottsdaleaz.gov/scottsdale-stadium', '1592156886', 'http://www.discountfirearmslv.com', 'http://www.homelife.ca/office_agents/2164', 'http://www.pillarwestgate.com', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', 'http://www.treasureisland.com/restaurants/little_richies.php', None, 'https://noracleveland.com', 'http://www.cabelas.ca/find-a-store/calgary/14', 'http://www.nevadagastro.com', 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'https://www.extraspace.com/storage/facilities/us/arizona/chandler/1000000272/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', '1592156922', 'http://www.big4motors.com', 'http://telemindclinic.com', 'https://www.wildblue.studio', 'http://theistanbulgrille.com', 'http://www.dunkindonuts.com', 'http://www.fluorescentnails.com', None, 'http://www.leveloneaz.com', 'http://www.summitmedicalweightloss.com/', 'http://hopesbridalnc.com', None, None, 'http://www.meninkilts.com/calgary', 'http://www.harkins.com', None, None, None, None, None, None, 'http://www.marriott.com/hotels/travel/cltfm-fairfield-inn-and-suites-charlotte-matthews/', 'http://luvcuts.com', 'http://www.toronto.ca/parks/parks_gardens/allangdns.htm', 'http://www.abrazadental.com?utm_campaign=local&utm_medium=citations&utm_source=yext', None, None, 'https://www.take5oilchange.com/locations/oh/mayfieldheights-130/', '1592157006', 'https://www.ihop.com/en/restaurants-gilbert-az/920-s-gilbert-rd-1529', 'http://www.murillocarpet.com/', 'https://www.levinfurniture.com/furniture-store/pa/pittsburgh/5438-baum-blvd', None, 'http://www.stanfordcapitalloans.com', 'http://www.jpgexhaust.com', None, None, None, 'http://www.cpr4yourcar.com', 'http://lulyssalonllc.weebly.com/', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/328+Cochran+Road-Mount+Lebanon-PA-15228/storeid=5094?cid=ps_ylp_2020', 'https://www.macu.com/branch-locations/az/gilbert/gilbert-branch/0146', None, 'http://www.JimmyJohns.com', 'http://www.cpr-savers-training.com', 'https://www.paviliondentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.trane.com/residential/en/buying-a-trane/find-a-dealer.html/401830', None, None, 'http://www.carvel.com', 'http://baliandbeyond.ca', 'http://www.karaokerentalphoenix.com', 'http://www.eggsmart.ca', None, None, 'http://www.vogava.com', 'http://www.mrcookschinesecuisine.com', None, 'http://streetsofnewyork.com/', None, 'http://www.truphysicaltherapy.com', 'http://savagewalker.com', 'http://www.tntauctionssnelgrove.com/', 'http://goodworksautorepair.com', 'http://www.hikethislasvegas.com/', 'http://www.pacificforesightsecurity.com/free-security-yelp', None, 'http://www.oneluckypup.com', 'http://www.stovalldentistry.com', 'https://www.dominos.com', None, 'http://www.plushsalonaz.com', 'https://www.kaizenprogressivehealth.com', 'http://www.stoppleworthplumbing.com/', 'http://www.customfitdj.com', None, 'http://www.autodealzaz.com', None, 'http://www.smoothieking.com', 'http://floweramaofglendale.com/', 'http://benedictinewomen.org', None, 'http://www.purevanityspa.com', 'http://www.salonentro.com', 'http://www.shell.us/', 'https://canyonstateclassics.com/contact', 'http://Slicersonmain.com', 'http://www.1brotherspizza.com', None, None, 'https://www.aa.com', None, 'http://www.drlfish.com', 'http://dowdentalcare.com', 'http://www.dignitymemorial.com/funeral-homes/mesa-az/melcher-mortuary-mission-chapel/4527', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.rotorooter.com/scottsdaleaz', 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', None, None, 'https://kottasushi.ca', 'http://www.medvetforpets.com/location/medvet-akron/', 'http://www.internationalhotel.ca', 'http://www.lonemortgage.com', None, 'https://toothworks.com/toothworks-bay-adelaide-dental/', 'http://www.steves-auto-service.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.valleyhomepros.com', 'http://www.smallbarclt.com', None, 'http://www.toscanacondorentals.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281379878&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'https://www.goldbergcentre.com', 'http://www.roosterskountrykitchen.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89102/838069/', 'https://www.altierus.org/campus/henderson', 'http://www.coach.com', 'https://medmen.com/stores/scottsdale-north-scottsdale-airport', 'https://hihidonuts.business.site', 'http://www.bulwarkpestcontrol.com/', 'http://ranchoflooringvegas.com', '1592157278', 'http://www.JimmyJohns.com', 'https://www.phoenix.gov/publicworks/garbage/disposable', None, 'http://singsing.com', 'https://aestheticrevolutionlv.com', None, 'https://www.pimtmassage.com', 'http://www.cocosbakery.com/', 'https://www.capriottis.com', 'http://acewasherservice.com/', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'https://www.socialsecuritybranch.com/nv/henderson/henderson-social-security-office/10416-s-eastern-avenue/', 'http://www.collisionrepairphoenix.net', None, None, None, None, 'https://www.olivegarden.com/locations/az/scottsdale/scottsdale-e-cactus-rd/1234?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:scottsdale-az-1234_pl:locurl_rd:1175', 'http://www.jimscoins.com', None, 'http://serenitycleaningaz.com', 'http://www.reddoorliving1.com/delta-lakewood/', 'https://rdavis.amerifirstloan.com', None, None, None, None, 'http://www.tbdnursery.com', None, 'http://www.thescottresort.com/?utm_medium=enhanced-profile&utm_source=yelp', 'https://www.hafezpersianrestaurant.com', 'https://www.zaxbys.com/locations/ga/monroe/195-martin-luther-king-jr-blvd/', 'http://www.yetifirearms.com', None, 'http://www.bombaypalacetoronto.com', None, 'http://lebanesebakery.ca/', 'http://www.midabui.com', 'http://www.whoolisbarandgrill.com', 'https://www.yourcupcakequeen.com', 'http://www.banfield.com/veterinarians/pa/monroeville/moe?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://www.vannormanlaw.com', 'http://www.eaglehomeinspections.net', 'https://www.anytimefitness.com/gyms/372/Huntersville-NC-28078/?utm_source=yelp&utm_medium=local', 'http://oralsurgeryaz.com', None, 'http://www.cyclevegas.com', 'http://www.masteryoon.net', 'https://www.brighton.com/viewstore/123', None, None, '1592157435', 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://www.soundplumbinglv.com', 'https://www.envision1361.com', 'http://www.gurusweets.ca', 'http://rebathandkitchens.com', 'https://locations.theupsstore.com/pa/pittsburgh/4885-mc-knight-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.nikolastreeservice.com', 'https://www.doctorallenwellness.com', None, 'https://www.dominos.com', 'https://www.ncfdentistry.com', 'http://www.vervehairdesign.com', None, '1592157478', 'http://www.lossombreros.com', '1592157484', None, None, 'https://local.fedex.com/az/tempe/MSCA/', None, 'http://www.ilovesushihenderson.com', 'http://www.okraaz.com/', 'http://www.starbucks.com/store/9298/', 'http://mascariauto.com', 'http://www.azdanceproject.com/', 'http://www.thetilestore.ca', 'http://www.germancarscottsdale.com', 'http://fracturedprune.com/location/shops-norterra', 'http://tasty-chinese.com', 'http://www.haydeedocasarmd.com', None, 'http://bubblesandsqueak.com', 'http://www.greatclips.com/salons/6225', 'https://www.unclelouie.com', None, 'http://www.firemeupaz.com', '1592157549', 'https://www.hilton.com/en/hotels/lasdmhw-homewood-suites-las-vegas-city-center/?SEO_id=YELP-HW-LASDMHW', None, None, '1592157562', 'https://yonge-and-eglinton.orangetheoryfitness.com?utm_campaign=yelp&utm_term=072017&utm_medium=print&utm_source=redirect&utm_content=yelp_print', 'http://www.beerexpressisbest.com', None, None, 'http://www.omahasteaks.com/stores', None, 'http://www.commonwealthbar.ca/', 'http://www.silverminesubs.com/', 'http://www.presotea.ca', 'http://www.myharu.ca', 'http://www.piedmontgoldexchange.com', '1592157598', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://crclasvegas.com', 'http://www.wildwingrestaurants.com/franchisees/newmarket-north/', 'http://www.apples4you.com/', None, None, 'http://www.marinersmadison.com/', 'http://www.century21.com', 'https://www.mcdonalds.com/us/en-us/full-menu/123dollarmenu.html?cid=PS:GCM_MOP:NB::Yelp:All', 'https://www.choicehotels.com/CN387?mc=blypypaf', 'http://www.vegasinkandtoner.com/', 'http://www.johnvarvatos.com/storedetails?StoreID=5656', 'http://www.westsidecommunitymarket.org', 'http://richnerair.com', None, 'https://www.kwiktrip.com', '1592157649', 'http://www.starbucks.com', 'http://www.timhortons.com', None, 'https://www.thejoint.com/north-carolina/huntersville/birkdale-12006', 'http://www.lukehousemadison.org', 'http://www.greatclips.com/', 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', None, 'http://www.smokeandjoelounge.com', None, 'http://botecolv.com', 'http://www.keelinglawoffices.com', 'https://puredentalaz.com/home.htm', 'https://www.thewestlake.ca', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.greyhound.com/social?utm_source=Book%20now&utm_medium=Yelp&utm_campaign=permanent%20link%20', 'http://aaronmachineshop.com', 'http://www.vegasprohvac.com', None, None, None, 'http://www.torontoimageworks.com', None, None, 'https://desertrad.com/locations/southwest-wynn-road', None, 'http://rocksolid-surfaces.com', None, None, 'https://www.lappeneyecare.com', 'https://www.bentosushi.com', 'http://www.drrusselo.com', None, 'http://www.dunkindonuts.com', 'http://nouveauxclt.com', None, None, 'http://Pizza-wings.com', 'http://tracysautobody.com', None, None, 'https://www.marquiscompanies.com/facility/marquis-plaza-regency/', 'http://www.nascarspeedpark.com/nc.aspx', None, None, 'https://www.gowireless.com/store/stores/Arizona/Mesa/Mesa---MonteVistaVillageCenter----602609', 'http://www.kwikfill.com', 'http://www.usps.com', 'http://www.dolcegelato.net', 'https://www.hilton.com/en/hotels/pitokhx-hampton-pittsburgh-university-medical-center/?SEO_id=YELP-HP-PITOKHX', 'http://www.exclusivetailoring.com', 'https://www.martinandmacarthur.com/', None, 'http://www.marleypark.com/', 'http://www.corepestsolutions.com', 'https://www.marcustheatres.com/', 'https://www.dippindots.com/loc/ll/US/NC/Charlotte/6801-Northlake-Mall-Dr_', 'http://www.healthydentalalternatives.com', 'http://www.northmountainvisitorcenter.org', '1592157819', None, 'https://www.fjtesq.com/?npcmp=dir:local:4407007:89145', None, '1592157829', 'http://www.mwuclinics.com', 'http://www.windowprollc.com', 'http://www.azairductcleaning.com', None, 'http://www.aamcolasvegas.com', 'http://www.casinonight2you.com', None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.dairycream.org/', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_426', 'http://www.ntb.com/store/8522/bedford-oh-44146-2252?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, 'http://www.lovebailbonds.vegas', 'http://downtownfood.ca/', '1592157877', '1592157879', None, 'http://www.apollos.com', None, None, 'http://www.dairyqueen.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://bennysva.com', 'http://urbantealoft.com/', None, None, 'http://www.25celciusbeautybar.com', 'http://www.simplicitylaser.com/locations/nevada/henderson/', 'http://www.hopkinsautospa.com', 'http://www.junk-rite.com', 'https://locations.dennys.com/NV/LAS-VEGAS/247828', None, 'http://www.arborealty.com', None, 'http://www.9dragonskungfu.com/', None, 'https://www.storquest.com/self-storage/az/tempe/9052', None, 'http://www.nailswithlovelv.com', 'http://www.daveyplumbingpittsburgh.com', 'https://birdysoulfood.com', 'http://motorsandmoreinc.com', None, 'http://www.steaknshake.com/locations/24097-steak-n-shake-us-hwy-17-s-brunswick', 'http://surprisefamilymedicine.com', None, 'http://www.czcustom.com', 'http://Dogfather.me', 'http://clickserve.dartsearch.net/link/click?lid=43700006430792752&ds_s_kwgid=58700000444978432&ds_url_v=2', 'http://www.kelseys.ca/location_region.php?province=on&s=1&city_drop=North+York', None, 'http://jianphoto.com/', 'http://www.worldofdecorauctions.com', 'http://www.goodwillsp.org/shop/retail-stores/pineville/', None, None, None, 'http://www.childrensorchard.com/stores/las-vegas-nv/', None, 'https://www.walmart.com/store/3473/las-vegas-nv/whats-new', 'https://www.pescadoborracho.com', 'http://www.spiceshack.ca', None, None, None, '1592158252', None, None, None, 'http://www.extendasuites.com', None, None, 'http://www.docautorepairs.com', 'https://www.signaturestyle.com/locations/oh/medina/famous-hair-medwick-marketplace-haircuts-67153.html', None, '1592158276', None, 'https://www.luxor.com/en/nightlife.html', '1592158284', 'http://www.southstburger.com/location/35-first-commerce-dr/', None, 'http://shopmelrosevintage.com/', 'http://www.mrsub.ca', 'https://imwireless.net/locations/concord-ma/', 'https://lasvegaspainreliefcenter.com', None, 'https://www.extraspace.com/storage/facilities/us/arizona/mesa/501578/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.fastfreshfoods.ca/', None, 'http://www.zazaespressobar.com', 'http://www.snapfitness.com/gyms/lasvegas-nv-89147/7089', 'http://www.forever21.com', 'http://www.ssmokincafe.com', None, None, None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Carnegie-PA-15106/067741/', 'http://www.saloncafe.net', 'https://www.blumenailsspasolon.com', 'http://www.gehendricks.com/', 'https://www.norfolkhall.com', 'http://missionptaz.com', 'http://www.visithenderson.com/todo/special-events/stpatricksdayparade', 'http://www.skinapeelbeautybar.com', 'http://www.ccdcranch.com', 'http://www.craftdogs.com/', None, 'http://www.tomatoesiipizzeria.com/', 'http://yesidobridals.com/', 'https://www.lumberliquidators.com/ll/stores/az/mesa/1845-south-power-rd?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1388', None, None, 'http://www.walmart.ca', 'http://www.papajohns.com', 'http://www.partycity.com/storedetail.do?id=842', 'http://locations.tccrocks.com/az/scottsdale/8980-e-indian-bend-rd.html', None, None, None, '1592158380', 'http://www.raxlenpharmacy.com', 'http://www.anjapparcanada.ca', None, 'http://www.dennys.com', 'https://www.ispynserve4u.com', 'http://mainstreetautoservices.com', 'http://www.dennyscarwash.com', None, 'http://www.bk.com', 'http://www.eatgenos.com', None, 'https://www.seeeyewear.com/locations/pittsburgh', None, 'https://www.piesbyinge.com', 'https://locations.nekterjuicebar.com/ll/US/AZ/Tempe/2000-E_-Rio-Salado-Pkwy_*-Ste_-1213?utm_source=yelp&utm_medium=link&utm_campaign=Tempe&utm_content=URL', 'http://kohinoortempe.com', 'http://idolizespa.com', 'http://www.naturaltress-salon.com', 'https://www.sunrisepreschools.com/locations/baseline-gilbert/?utm_source=yelp&utm_campaign=online_listing_gilbert_280&utm_medium=referral&utm_term=business_url', None, None, 'http://www.peridotsweets.com/', None, 'http://www.thefitmenswear.com', 'http://thegrillat11union.com', 'http://www.papajohns.com/', None, 'https://www.victoriassecret.com', 'http://www.lostdutchmanroasters.com', 'http://www.petplanethealth.com/stores/village-plaza/', None, None, 'http://www.upinvapor702.com', 'https://www.ronmarhoferchevy.com', None, None, 'http://www.sanealcamera.com', 'https://www.bankofamerica.com', 'http://www.thesinginglady.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006435127049&ds_s_kwgid=58700000444950373&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.arizonaeyecenter.com', None, None, 'http://www.thespicetrader.ca/', None, None, 'http://www.harkinstheatres.com/', 'https://chefmayra.com', None, 'http://www.westmore.ca', None, 'http://www.LaRoccaKitchen.com', 'http://www.craquedecreme.com', 'https://heartandlungnv.com/physicians/profile/Arnold-Chung-MD', None, 'http://www.loveandkissespetsitting.net', None, None, 'http://www.tsgservicesaz.com', 'https://www.staples.com', None, None, None, 'http://carlosthecomputerguy.com/', 'http://info.tradesecrets.ca/locations-reviews/upper-canada-mall/', None, 'https://www.shapirolawaz.com', 'http://www.azpatiocover.us', 'http://bevvyuptown.com', 'http://Www.solasalonstudios.com/salon-professional/liz-mervar1', None, 'http://www.yangschicken.ca', None, 'http://www.dsw.com', None, None, 'http://birdhauscoffee.com', None, 'http://www.jysk.ca', None, 'http://www.puffnstuffstores.com', 'https://www.brakesplus.com', 'https://locations.noodles.com/pa/pittsburgh/476-mcmaster-way.html', 'http://www.michaeltoddsfurniture.com', None, 'http://www.dentistryintoronto.com/', 'https://jmichaelrealestate.com', None, 'https://splittingtimber.com/axe-throwing-phoenix/', 'http://www.crabhouselv.com', None, 'http://wisconsincutlery.com/', None, 'http://www.jerseygiant.ca', 'http://www.mazdaofrichmondhill.com', 'http://www.quiktrip.com', 'http://www.dimsumchineserestaurant.com', 'http://www.marcustheatres.com', None, 'http://kaiburcoffee.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.shishaliciouscafe.ca', None, 'http://charandamexicaneatery.com', 'http://www.rideprlimo.com/scottsdale-limousine/', 'http://www.distillata.com', 'http://www.sobeys.com/en/stores/sobeys-aurora-bayview/', 'http://www.acanac.com', 'https://www.ubreakifix.com/locations/goodyear', 'https://www.robainalaw.com', 'http://www.newdimensionsauto.com/', 'http://www.martinmarineaz.com/', None, None, 'http://www.rexall.ca/', 'http://www.baierlhonda.com', 'http://www.pizzalafelice.com', None, 'https://www.olivegarden.com/locations/wi/madison/madison-east-towne-mall/1300?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:madison-wi-1300_pl:locurl_rd:1227', 'https://www.chilis.com', 'http://www.npfy.org', 'http://www.bedbathandbeyond.com', 'http://www.andersons.pub', 'https://www.lowes.com/store/AZ-Scottsdale/1850', 'http://www.playfactoryparty.com', None, 'http://cityh2o.com', 'http://www.zooecomuseum.ca/', 'http://www.shamsflorist.ca/?srccode=yelp_track', 'https://massagetherapistscottsdale.com', 'http://www.wilshirepines.com', 'http://www.modernfurniturestudio.com', 'http://allontarioapplianceclinic.ca', 'http://www.bridalalterationspittsburgh.com/', 'https://perfumecollection.ca', None, 'https://www.homedepot.com/l/Ray-Road/AZ/Chandler/85226/476?cm_mmc=seo-yelp&', 'http://www.bornandraisedlv.com', None, 'https://www.statefarm.com/agent/us/nv/las-vegas/ladonna-koeller-p89cl1ys000?cmpid=jxep_blm_0006', 'https://www.jewelrymedinaohio.com', 'https://eastendpittsburgh.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'https://www.choicehotels.com/wisconsin/madison/cambria-hotels/wi143/rates', 'http://www.cafe-mirage.com', None, 'http://adagestudios.com', 'https://www.masteroftintllctempe.com', None, 'http://lsmchiro.com/clinics-office-hours/sunprairie.html', 'http://plumbing-repair-now.com', 'http://spookysswirls.com', 'http://www.sunserimove.com', None, 'http://www.nandos.ca/restaurants/bay-street', 'http://www.massageheights.com/south-pointe-plaza', 'http://www.a-zsources.ca', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', 'http://www.smilereef.com', 'http://simplycardio.com', None, 'http://kismetandclover.com/', 'http://www.assouline.com', 'http://www.pkcreek.ca/', 'http://www.internationalgalleriesurbana.com', 'http://www.regularsbar.ca', 'http://www.6DegreesAZ.com', 'http://www.oldnavy.com', None, 'http://www.dmcsystemsllc.com', 'http://www.jumpstartchildcare.com', None, 'http://www.villapizza.com', 'https://www.yourlistingexpert.com', 'http://stores.dsw.com/usa/nv/henderson/dsw-designer-shoe-warehouse-stephanie-street.html', 'https://www.usps.com/', None, 'https://eastvalleyrv.com', None, '1592158816', None, None, None, 'https://www.aircanada.com/ca/en/aco/home/fly/premium-services/maple-leaf-lounges/maple-leaf-lounge-details.html#/!lounge@toronto', 'http://chickswithspiritualgifts.com', None, 'http://www.costco.com/', '1592158831', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.tyddvegas.com', 'http://www.samfawazphotography.com', None, None, 'https://www.schendelpest.com', 'http://www.honeybeeac.com', None, 'https://www.gavishpropertymanagement.com', 'http://www.topnailsaz.com', 'http://www.katesissons.com', 'http://www.JimmyJohns.com', 'https://plexustechnology.com', 'http://www.thedirtydrummer.com', 'http://pac.unlv.edu/index.php', 'http://www.enterprisecarsales.com/location/5482/Enterprise_Car_Sales_Las_Vegas?mcid=iyp:277&CUR=yelp', 'http://www.happitimedaycare.com', None, '1592158875', 'http://www.wyldewoodillinois.com', None, None, 'http://www.tribridpersonaltraining.com', 'http://www.kw.com', '1592158885', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.azheart.com/', None, 'http://www.bellabridesmaids.com/', 'http://www.dollargeneral.com/', None, 'http://www.plazahotelcasino.com/entertainment/the_best_little_wh', 'http://www.yofreshyogurtcafe.com', 'http://mdskinlounge.com', None, '1592158911', 'https://www.itdrsolutions.com', 'https://www.papajohns.com', 'http://hiltongardeninn3.hilton.com/en/hotels/ontario/hilton-garden-inn-toronto-oakville-YTOTVGI/index.html?SEO_id=YELP-GI-YTOTVGI', None, 'https://www.emser.com', 'https://locations.jackinthebox.com/us/ca/glendale/1200-w-glenoaks-blvd', None, 'http://www.pitapitusa.com/', None, None, None, 'http://www.tlcdentalcarelv.com', None, 'http://www.chiefsautowash.com', 'https://www.gamesourceinc.net', None, None, None, 'http://www.bigotires.com/Locations/89032', 'http://www.mbenergetics.com', None, '1592158958', '1592158961', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.goldenchinarancho.com', 'http://www.starbucks.com/store/14175/', 'https://www.cellphonerepair.com/monroeville-pa/', 'http://vbarbershop.com/locations/kierland-scottsdale/', 'https://agents.allstate.com/padma-schaudt-las-vegas-nv.html', 'https://www.petsmart.ca/stores/ca/on/oakville-store2002.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', '1592158979', 'http://www.designedbydyani.com', 'http://spadinaoptometry.ca/', 'https://www.wellschiro.com', 'https://www.justonemoretavern.com', 'https://www.sprouts.com/stores/details/-/store-details/view/store/7/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.framestorepittsburgh.com', None, 'http://totemappliance.com/', 'http://www.silvertoncasino.com', 'http://playnwisconsin.com', 'http://www.tokasticksgolf.com/index.php', 'https://local.biglots.com/nv/las-vegas/4500?zcp=pd_local_yelp', 'https://www.dwellarizona.com', 'http://achermanlaw.com/', 'http://www.odellconstructioninc.com', None, 'http://www.thebownesiangrocer.ca', 'http://outlandcigars.com', 'http://stlouiswings.com', 'http://www.brokeassphone.com/broke-ass-phone-locations/broke-ass-phone-rocky-river-ohio', 'https://www.valleywidecooling.com', None, 'http://www.amrracing.com', 'http://www.cmlibrary.org/locations/branches.asp?id=13', None, 'http://nakedpizza.biz', 'http://www.meltinyourmouthcupcakes.com', 'https://local.fedex.com/az/phoenix/office-5048/', 'https://locations.usbank.com/index/arizona/gilbert/east-baseline-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.dominos.com', 'http://www.treeworkersofphoenix.com', 'http://d-moes.com/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://dansdogsdiner.com', 'http://www.saucepizzaandwine.com/locations/scottsdale-scottsdale-waterfront/', None, 'http://Www.tomjames.com', 'http://www.healinginspirations-wi.com/', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', '1592159067', 'https://stores.advanceautoparts.com/pa/etna/500-butler-street?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', None, 'https://local.fedex.com/nc/charlotte/office-0746/', 'https://northvalleysurgerycenter.com', 'http://www.burritozone.ca', 'http://www.enterprise.com/car_rental/deeplinkmap.do?cnty=US&gpbr=53W9&bid=004&arc=YAPL100&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://pddlv.com', 'https://hairbykee.wixsite.com/hair-by-kee', None, None, '1592159093', 'http://www.trianglebarswissvale.com', None, None, None, 'http://freshco.com/stores/bloor-dundas', 'http://www.bojangles.com', 'http://www.mark-taylor.com/arizona/san-sonoma/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.midhafurniture.com', None, None, 'https://www.lashandskinlab.com', None, None, None, None, 'http://www.serviceking.com/locations/service-king-bell-rd?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', None, None, 'http://alatisinspectionservice.com/lp/home-inspection', 'https://www.moes.com/find-a-moes/pennsylvania/bridgeville/938?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', None, 'http://www.wagg-n-walk.com', 'http://www.clevelandcabby.com', 'https://www.chaoshomeloans.com', 'http://www.marondahomes.com', 'http://www.morocochocolat.com/', 'http://anytimefitness.com/North-Royalton', 'http://qualitysystemsac.com', 'https://local.safeway.com/safeway/az/sun-city-west/13503-camino-del-sol.html', 'http://www.buckinghamsports.ca/view/buckinghamsports/the-penalty-box', 'http://geckohomeservices.com', 'http://www.republicwesthome.com', 'http://www.pawlorpets.com/', 'https://www.sevabeauty.com/location/az/avondale-w-rancho-santa-fe-blvd/', 'http://www.tjmaxx.com', None, None, 'http://www.barleyhousecleveland.com/', 'http://www.landmarkcinemas.com/bolton/contact-us', '1592159181', 'http://www.irenevoo.com', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', None, None, None, 'http://www.cumbraes.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://www.curtisnewsomedds.com', 'http://walmart.com/', 'https://www.scottsdalemoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://www.casinomontelago.com', None, None, None, 'http://www.jaguarnorthscottsdale.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Mesa-AZ-85210/723081/', None, 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1368', None, 'https://www.viomedspa.com', 'http://www.paradisetileandnaturalstone.net', None, 'http://www.kinglawofficespc.com', 'http://www.innovateframe.com', None, 'http://www.happyhourarizona.com/champions-sports-saloon', 'http://www.millcrestpark.com', 'http://www.atlanticbay.com', 'http://www.fiddlersdream.org', 'http://www.nationaleventstaffing.com', 'http://holisticfit.life', 'http://www.atwistedtulip.net', 'https://www.carmax.com/stores/7284?adcode=YLP7284&utm_campaign=LG_AFF&utm_source=LG_AFF_YLP&utm_medium=local&utm_content=shop', None, None, None, 'https://stewardship.pro', 'http://www.golfsmith.com', 'http://www.duskscottsdale.com', None, 'http://www.metrosouthbridge.com', 'http://www.pizzahut.com/', 'http://www.80OnGibsonapts.com?campaign_code=yelp_80_On_Gibson_NV_89012', 'http://reliableappliance.ca', 'https://www.legendsofchampaign.com', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=101357', None, None, 'http://www.spotlesssquadlv.com', None, 'https://asquaredmathtutoring.com', 'http://www.autoxpertslv.net', None, 'http://www.shanklelaw.com', None, 'http://www.cajuncrawfishLV.com', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1165', 'https://ohiosbestmassage.com', 'https://handandstone.com/locations/az-glendale', '1592159307', '1592159309', 'http://inesdisanto.com/', 'https://www.mandalaybay.com/en/nightlife/eyecandy-sound-lounge.html', None, 'http://affordablemoverslv.wixsite.com/website', None, 'https://pizzapit.biz', 'http://www.piedmontexpresscaresuttonroad.com/', 'http://www.distinctiveweddingvideos.com', None, 'https://affderm.com/locations/tempe-office/', 'http://vegasproperty.management', 'http://www.gandmstaffingsolutions.org/', 'http://www.bellagio.com/attractions/gallery-of-fine-art.aspx', 'http://www.structube.com', None, 'http://www.autocash.com/auto-cash-in-las-vegas?utm_campaign=places&sf_traffic=paid_listing_yelp&utm_medium=listing&tmx_id=d2c199521a9a9f&utm_source=yelp', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.theavenuebanquethall.com', None, None, None, 'http://trutea.ca', 'http://www.rbomotorsports.com', None, '1592159362', 'http://thebagelshoppe.weebly.com/', 'http://www.freewayinsurance.com', 'http://www.persianbijar.com', 'https://www.phoenixmusiclessons.com', 'http://www.discoverydetectivegroup.com', 'http://www.fortinos.ca/en_CA/storedetail.484.html', 'http://www.motel6.com/reservations/motel_detail.aspx?num=4742', 'http://www.its2di4.com', None, 'http://pawminderspluspetsitters.com', 'http://www.fiatusaofstrongsville.com', 'http://www.skinsopretty.com', 'https://www.ontario.ca/page/serviceontario', 'http://www.northphoenixcampground.com', 'http://www.packbrotherscollisioncenter.com/', 'http://www.gusnewyorkpizza.com/', None, 'http://www.canadianpardons.ca', 'http://www.computerezearizona.com', None, 'http://www.vashticosmetic.com', None, 'http://fitforlifefood.com/', 'https://www.meijer.com/shop/en/store/307/?cmpid=OLA:040319:YelpGrocery', None, 'http://www.suepembertoneducation.com', 'http://www.disktopia.com', 'http://www.wjbonline.com', 'http://www.atriasrestaurantpncpittsburgh.com', 'http://www.discotech.me', 'http://www.myturnlv.com', None, 'http://www.catchacritter.us', None, None, 'http://www.ourfamilyeyecare.com', 'http://www.goodwillaz.org/', 'http://www.BroadstoneParadiseValley.com/?utm_medium=listing&utm_source=yelp', 'http://uptownnailsalon.wix.com/uptown-nail-salon', 'https://www.sticyyc.com/locations-1/', 'http://www.harveyswineburger.com', 'http://esoslifestyle.com', 'http://www.smithenvironmentalsolutions.com', 'https://beyondextensions.mayvenn.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.cardinalewaymazdapeoria.com/?ibp-adgroup=yx_target', None, '1592159462', 'https://local.albertsons.com/az/peoria/8240-w-deer-valley-rd.html', None, 'http://www.plastikwrap.com', 'https://www.petsuppliesplus.com/Store/OH/Lakewood/Lakewood/128', 'http://www.thunderbirddental.com', 'http://poolservlv.com', 'https://www.heinens.com/Heinens-of-Hudson', 'http://www.jackscornertaplkn.com/', None, None, 'https://www.wyndhamhotels.com/hotel/03725?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:03725', 'https://innovativecleaningsvs.com', 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', 'http://www.statusinkllc.com', 'http://bellagiopizza.ca', 'http://www.puptowncharlotte.com', None, 'http://www.starbucks.com/store/10311/', 'http://avis.com', None, 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', 'http://aftbar.com/', 'https://local.skechers.com/az/phoenix/', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.autozone.com/locations/az/peoria/8669-nw-grand-ave.html', 'https://smartmoveinsurance.com', None, None, 'http://www.the-idea-store.org', 'http://www.dunkindonuts.com', 'https://www.i9sports.com/ProgramDirector/309/', 'http://www.rainrestaurant.ca', 'http://www.davidandgoliathtees.com/', 'http://www.starrdickensortho.com/', 'http://mickeles.ca/', None, 'http://www.westsidelaser.ca', 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?STORE=629&language=EN', 'https://gilbert.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, 'http://www.pitapit.com', 'http://www.cottonwoodstationeatery.com', 'http://superdiscounttrans.com/', '1592159557', 'http://www.bowlingwithleverage.com', 'http://www.saloncentric.com/', 'https://www.carolinashealthcare.org/locations/detail/carolinas-healthcare-urgent-care-union-west', 'http://www.autosonic.ca', None, 'https://www.heirloomtoronto.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.66065.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:66065', 'http://philipsplastics.com/', 'http://www.bookmans.com', 'http://www.wordofmouthdentistry.ca', 'http://www.starbucks.com', None, 'http://www.yofreshyogurtcafe.com', 'http://www.breadheadslv.com', 'http://www.luxor.com/attractions/attractions_king_tut_museum.aspx', 'http://www.crazymocha.com', 'http://www.vuaurology.com', 'http://www.costco.com/', 'http://www.mydcdental.com', 'http://www.ritzcarlton.com/en/hotels/charlotte/dining/punch-room', 'http://phoenicianestates.com/', 'http://www.bountifulfruitarrangements.com', '1592159602', None, None, None, None, None, 'http://www.azpowerwashpros.com', 'http://www.fishcreekvets.com/', 'https://haircutmensoutheuclidoh.com', 'http://Www.mixnmatchausa.com', None, 'http://consolidatedauto.com', None, 'http://www.cookinsgroup.com', 'https://stores.bestbuy.com/il/champaign/2117-n-prospect-ave-46.html/?loc=ns100&ref=NS', 'http://www.nextcare.com/locations/az/peoria-glendale/?utm_source=Yelp&utm_medium=Local&utm_campaign=peoria_glendale', 'http://darkhorsesportsbar.com', None, None, 'http://www.catseyevintage.ca', 'http://www.searsgaragedoors.com', '1592159643', 'http://www.westcoastkids.ca', 'http://heavenlyhairbodysalon.com', None, None, None, '1592159653', 'http://www.cyclonespitas.com', None, None, None, 'http://www.valledelsol.com', None, 'http://www.villageinn.com/', None, None, None, 'http://www.tascsolutions.org/locations/phoenix-central', 'http://hooverdamstore.com', None, 'http://www.elitepodiatry.net', None, '1592159685', 'http://www.cleverchefscatering.com/', 'http://www.successjustclicks.com', None, 'http://www.theterracegardens.com', 'http://www.nortownfoods.com', '1592159695', None, 'http://www.chinadragonbedford.com', 'http://www.choiceautorepairaz.net', 'http://gpsandtrack.com', 'http://www.pancheros.com/locations/tempe', 'http://www.oldvegastavern.com', 'https://store.vioc.com/wi/madison/3594-e-washington-ave-53704-GR0030', '1592159710', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.youfit.com/gym/scottsdale-scottsdale-rd-7346?utm_source=local&utm_medium=yelp&utm_campaign=club7346&utm_term=website', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.budget.com/', 'https://www.glamparlor.com/?utm_source=Yelp&utm_campaign=Main_Web', None, 'http://www.balanicustom.com/custom-suits-cleveland/', None, 'http://www.cox.com', 'http://www.westendcomics.ca', 'http://www.greenhousemontessorischool.com', 'http://carpetwarehousecleveland.com', None, None, 'http://www.ontrac.com', None, 'http://www.jacobsonbrosdeli.com', 'http://www.altrahomedecor.com', None, None, None, None, 'https://p3hp.org/nevada/p3-medical-group/our-locations/business-park/', 'http://lvmpd.com/', None, None, 'http://www.fastforwardskate.com', 'http://www.midoco.ca', None, None, 'https://www.starbucks.ca', None, None, 'http://www.dunkindonuts.com', 'http://www.findyourcenter.com/', 'http://www.neocoffeebar.com', 'http://www.locksmithbetty.com', None, None, '1592159796', 'https://www.walgreens.com/locator/walgreens-4667+william+penn+hwy-murrysville-pa-15668/id=11768', 'http://www.thespa-sunprairie.com', 'http://www.rushhourlegal.com', 'https://locations.jackinthebox.com/us/az/gilbert/4361-e-baseline-rd', None, 'http://www.celsiussushibar.com', '1592159814', None, None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', None, None, 'http://www.SonicAutoHouse.com', None, 'http://www.bayviewmooreauto.com/', 'http://www.jessicabashaw.com', 'http://www.thewoodenvine.com', None, 'https://merkatoethiopianrestaurantlasvegas.com', 'http://www.whitevacuum.com', None, None, None, None, 'http://www.beattheheatpoolservice.com', 'http://www.carmellaspizzagrill.net', 'http://www.tphc.ca', 'http://www.tomscountryplace.com', 'http://www.balaton-restaurant.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.autoexinc.com/', 'https://creativenailsandspascottsdale.com', None, 'http://www.canadiantire.ca/en/store-locator/ab/calgary-south-ab.store.html', 'http://rusticsocial.ca', 'http://wolfwatersports.com', 'https://www.extremearizona.com', 'http://www.theBooKnack.com', None, 'https://elementsmassage.com/fitchburg', None, 'https://www.copart.com/locationDetail/47', 'http://tigotrattoria.ca', None, 'http://www.nevadadesertmermaids.com/', 'http://www.caesarsuniforms.com', 'http://www.wingsntings.ca/', 'http://www.boulderzclimbing.com', 'http://www.SonoranVein.com', 'http://www.goodlifefitness.com', 'http://nievemalandra.com', None, 'http://www.scottsdalespice.org', None, 'http://l.macys.com/madison-wi?cm_mmc=Yelp_Stores-_-Madison-_-n-_-228&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Madison_228&m_ac=yelp_stores&m_ag=n', 'http://www.superiortire.ca/locations/mode/7/208-king-rd-oak-ridges-on-l4e2w1.aspx', 'http://thearizonafishingguides.com/index.php', 'http://www.chapmancollision.com/', 'http://www.quiktrip.com/', None, None, None, 'http://www.littlecaesars.com', 'http://www.onereddoorphotography.com', 'http://www.circuscircus.com/casino/slots_a_fun.aspx', None, 'http://www.milgard.com', 'http://benetflorentine.com', 'http://www.sbistroaz.com', None, 'http://locations.avis.com/us/az/chandler/c5a.html', 'http://www.rockcitydance.com', None, 'http://www.washwerksexpress.com', 'http://AutoFinanceNC.com', 'http://www.mrhandyman.ca/calgary-south', None, 'https://arizona.weidner.com/apartments/az/mesa/pala-mesa-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', None, 'http://www.lesterklebedpm.com', 'http://www.bk.com', 'https://www.bathandbodyworks.com', None, 'http://www.brakemasters.com', 'http://clearfloat.ca', None, 'http://www.watchdogpestcontrol.com', None, 'http://www.budgetbridal.vpweb.com', 'http://advancedheartcare.com/', 'https://moxies.com/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', 'http://www.ihlcanada.com', 'http://www.parmalaserwash.com', None, 'http://www.anatoliaturkishfood.ca', None, None, 'http://calgarylibrary.ca/locations/shaw', 'https://www.payless.com/stores-location/NV-LAS-VEGAS-5798.html', 'https://peoria.uptownjungle.com', None, 'http://www.rimrepairrx.com', None, 'http://www.apria.com', None, 'http://www.santinocatering.com', 'http://www.fusionsincsalonanddayspa.com', 'http://www.qualityonepool.com', None, 'http://zenarizona.com/', None, 'http://empireplumbingac.com/', 'http://www.contourmedical.com', 'https://website-18496976604484669992-seafoodrestaurant.business.site', 'http://www.swimmingpoolrepairphoenix.com', 'https://locations.visionworks.com/ll/US/OH/Beachwood/26300-Cedar-Rd', 'http://www.barrebodystudio.com', 'http://www.wwsdental.com', 'http://robertostacoshop.com', None, None, 'http://pacificeastcoventry.com/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://www.labonitadulceria.com', 'http://www.retinalconsultantsaz.com', 'http://www.irideworldwide.com', 'https://titleboxingclub.com', 'http://www.serviceking.com/locations/service-king-north-las-vegas?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'https://www.elegance-living.com/senior-living/nv/las-vegas/wentworth-las-vegas', 'http://www.cafekrishnaaz.com', 'http://mountaincreektrees.com', None, 'http://www.batw.ca/', None, '1592160137', None, 'https://locations.vitaminshoppe.com/nv/lasvegas/vitamins-supplements-las-vegas-nv-394.html', None, None, 'http://www.secondsoleohio.com/#!akron/c1fn6', None, None, None, None, 'http://www.purpleorchidflowers.ca/', None, 'http://www.bluepandalv.com', 'http://calgary.treehouseplay.com/', 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'http://www.ncdot.org/dmv/', 'http://www.2meatballz.com/', 'https://www.fit4less.ca/locations/ontario/north-york/409?utm_source=yelp&utm_medium=cta&utm_term=torontolawrence-f4l', 'http://www.mrhero.com/', 'http://www.truevalue.com/', 'http://www.pombalensebakery.com/', None, 'http://www.peoriacpr.com/', 'http://www.terribleherbst.com/', None, 'https://www.smartstyle.com/en-us/locations/on/brampton/located-inside-walmart-3135-haircuts-5184.html', 'http://www.massagebymichael.vegas', 'https://www.myeyedr.com/locations/ballantyne?utm_source=Yelp&utm_medium=Referral&utm_campaign=ballantyne', None, 'http://www.reebokcrossfitramsay.com', 'http://blackowlrealtylv.com', 'http://www.speducci.com/', None, 'https://deadcityvegas.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://bostonpizza.com/centropolis-laval', 'https://satruck.org', 'http://www.richbeckguitars.com/', None, 'http://www.inspiringsmilesdentistry.com', None, 'http://www.morcillapittsburgh.com', 'http://www.kids-supergym.com', None, 'http://www.deserthottubs.com', 'http://www.dimaggiostire.com/', 'https://local.fedex.com/nv/las-vegas/office-1441/', None, None, None, 'http://budstreecare.com', None, 'http://www.saintsandsinnershairdesign.com', 'http://www.woodiesautoservice.com', None, 'http://www.gap.com?tid=gpme000290', None, 'http://rawfitnesslv.com', 'http://www.starbucks.com', 'https://cocosgelatooh.com', 'http://www.sissybeautysalon.com', 'http://m.primarycarewalkinmedicalclinic.com', None, None, 'https://www.sprint.com/storefronts/bd/sprint-matthews-nc-28105-fcs-2516/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.xiangcunfaxian.com/', 'http://Www.LVLegalHelp.com', 'https://scottsdale.andaz.hyatt.com/en/hotel/dining/weft-warp-art-bar-kitchen.html', 'http://www.salzmann.com', None, 'http://glossitdetailstudio.com/', 'http://www.trcaparks.ca', 'http://www.eastofchicago.com', None, 'https://chocolateshops.sees.com/pa/pittsburgh/chocolate_shops_pittsburgh_pa_pa-17.html', 'http://houseoffitness.net/', None, 'http://www.circletree.net', 'https://www.atmosphere.ca/stores/calgary.html', 'http://www.burgers2beer.com/', 'http://www.shipleyortho.com/', None, None, 'http://www.mamathaikitchenaz.com', 'http://www.junctionatantiquity.com', 'http://www.vendettatowing.com', None, None, 'http://www.centennialwellnesscenter.com', 'http://thebiomedcenter.com/', 'http://www.LandisReedHomes.com', 'https://www.thegibsoncharlotte.com', 'http://www.vientianepalacerestaurant.com', 'https://www.allauramedical.com', None, 'http://www.benefitcosmetics.com/?ext_id=yelp_ulta_010713_Yelp', 'http://www.cnroofing.com', None, 'http://www.sabas.com', 'http://www.greatclips.com/', 'http://www.mammothairlv.com', 'http://www.daleshirleys.com', None, 'http://www.baldwinbrothersautomotive.com', 'http://www.gyroworldohio.com/', None, None, None, 'http://www.bistro-jules.com', None, 'http://onsitebuilds.com/', 'http://www.livewellarborsteelecreek.com', 'http://www.augiessportsgrill.com/', None, None, 'https://www.gowireless.com/stores/az/gilbert/gilbert-gilbert-road/', None, None, 'http://www.arrabiatas.com', None, 'http://www.heroburgers.com', 'http://www.amesachiropractor.com', 'https://onginstitute.com', 'https://www.woodlandestatesapartment.com', 'http://www.bamboobakery.com', 'http://www.olsonglassandmirror.com', 'http://www.carolinafoxs.com', 'http://www.kingwongchinese.com', 'http://www.midaslocator.com/AutoRepairFinder/tabid/151/Default.aspx', 'http://www.theminderbinder.com', 'http://www.wpinsure.com', 'http://www.sagastasalon.com', 'http://velveteenrabbitlv.com', None, None, 'http://pesterminate.ca', 'http://downtown.muramoto.biz', None, 'http://nevadacheapcars.com/', 'https://www.laserquest.com/nv-lasvegas', None, None, None, None, 'http://smogbusters.com', None, 'http://www.theriverrockgrille.com', 'http://www.myresortspa.com', None, 'http://nalysfloralshop.com', 'http://www.plantitsucculent.com', None, 'http://www.greatclips.com/salons/1552', 'https://www.suburbanpropane.com/locations/phoenix-az/', 'http://www.windycityair.net', 'http://www.lavidamassageshadysidepa.com', None, None, '1592160519', 'http://www.upandawaylandscaping.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, None, 'http://www.sincerelyyogurt.com/locations/peters-township', 'http://www.classickids.biz', 'http://mastercrafttires.com/', 'http://glenwoodacresrvpark.com', 'http://forecloseduponpets.org', 'https://www.mediweightloss.com/locations/scottsdale?_ppc=Z8FWKRXKT5', 'http://galaxiedinerwoodbridge.com', 'http://yeoldsoapmill.com/touch', None, None, 'http://www.1866staydry.com', None, 'http://www.sarphx.com', None, None, None, 'https://homesbyclaudiamarion.kw.com', 'http://cloud9windows.com', 'http://www.bevmo.com', None, None, None, 'http://www.tailgatersilprimo.com', 'http://www.rainbow.travel', 'http://www.timhortons.com/', 'http://www.noblebeastpets.com', None, 'http://compadresmexicanrestaurantwi.business.site', '1592160596', '1592160598', 'http://www.sunnymorning.ca', None, 'https://www.westvalleytech.net', 'http://www.lasvegasbraces.com', 'http://www.cicispizza.com', None, None, 'https://stores.dickssportinggoods.com/az/phoenix/365/', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360123&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.gamestop.com', None, 'http://www.apple.com/retail/scottsdalequarter/', '1592160628', 'http://www.mark-taylor.com/arizona/san-marquis/?utm_content=visit-website&utm_medium=listing&utm_source=yelp', '1592160634', 'http://www.quiktrip.com/', 'http://www.yellowcheckercabchampaign.com/', 'https://www.lowes.com/store/PA-Monroeville/1660', 'https://megafurnitureusa.com', 'http://greenbeautyspa.com/', 'https://www.wyndhamhotels.com/hotel/52964?tel=18666154223&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52964', 'http://www.itsnewtomeconsignments.com', 'http://www.valueworld.net/', 'http://www.lunarossaristorante.com/', None, 'https://www.bannerhealth.com/locations/mesa/banner-urgent-care-1', None, 'http://www.planetfitness.com/gyms/willowick-oh-985?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://jakesautorepair.com/', None, None, 'http://www.flippnburgers.ca', 'https://camp.nc', 'http://www.lenotrebistro.com', None, 'http://www.yourfloorz.com', None, '1592160693', 'http://www.paradisejuice.com', None, 'http://www.nailsforyou.ca', 'http://www.vintagebymisty.com', None, 'http://www.chezcora.com', 'http://www.thehealthygreek.ca/', 'http://www.upmc.com/locations/hospitals/western-psychiatric/Pages/default.aspx', None, 'https://www.scottsdalecc.com', 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', 'http://www.tccarpetcare.com/', 'http://www.phohongnc.com', 'https://us.louisvuitton.com/eng-us/point-of-sale/usa/louis-vuitton-cleveland-saks?utm_source=yelp&utm_medium=organic&utm_campaign=store_listing_storepage', '1592160727', None, 'http://www.nice1nails.com', None, 'http://www.travelsuitesinn.com', None, 'http://priscillaspantrypetsupplies.business.site', None, None, 'http://www.avidalaserandspa.com/', None, None, 'http://www.city-tavern.com', 'http://www.lockquest.com', None, 'https://www.plannedparenthood.org/health-center/arizona/scottsdale/85251/scottsdale-health-center-2809-90030?utm_campaign=scottsdale-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', None, None, None, None, None, 'http://tirerepairlasvegas.com', 'http://www.tangdynastyurbana.com', None, None, 'http://www.thegridcl.com', None, 'http://www.janasredroom.com', 'http://atrackout.com', None, None, 'http://www.mancavecigarlounge.com', 'http://quicklaneoflasvegas.com/', 'https://locations.theupsstore.com/nv/north-las-vegas/5575-simmons-st?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://consulmex.sre.gob.mx/lasvegas/', 'http://www.azstoragedoctor.com', 'http://www.greenstreetcommunitiesinc.com', 'http://www.pcpropane.com', None, None, "http://charmeck.org/mecklenburg/county/ParkandRec/Greenways/OpenGreenways/Pages/MallardCreekandClark'sCreek.aspx", 'http://www.paradisevalley.edu/', 'http://www.curiouskidspreschoolaz.com/', 'http://www.gardenialanephotography.com', 'http://www.kandrpainting.com', 'http://bestestiedayspa.com', None, None, None, 'https://locations.panerabread.com/oh/hudson/118-w-streetsboro-street.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'https://www.usps.com/', 'http://www.apartmentsnow.online', 'https://www.5280mexicangrub.com', 'http://Destinations.rei.com/Arizona', 'http://www.ferrarimaseratioflasvegas.com', None, 'http://www.justrightlandscape.com', 'https://arizonapain.com/contact-us/chandler/', 'http://www.degnanlawaz.com', '1592160875', None, 'http://azvideomarketing.com', None, 'https://www.marks.com/en/stores/north-york-2625d-weston-road-14-15-crossroads-centre.html', 'http://toterafinefoods.ca', 'http://www.moonhaven.com/', None, 'http://www.torontoguesthouses.com', 'http://massagemaniaglendale.com', None, None, None, None, 'http://www.plannedparenthood.org/health-center/ohio/rocky-river/44116/rocky-river-health-center-2418-91230', None, 'http://www.totaltransit.com', 'https://www.marriott.com/hotels/travel/phxsh-springhill-suites-scottsdale-north/', 'http://www.skatenrd.com', 'https://blueboxmovingcompany.com', 'http://lamsaz.com', 'http://www.designsbylanae.com', None, 'http://arborstownhomes.com', 'http://www.europebound.com/', 'http://www.acehardware.com', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'https://azvent.com/locations/mesa.php', 'http://usacollision.com', None, 'http://www.falloutgames.net', 'http://www.shaanxibiangbiang.com', None, 'http://www.brettbaughman.com', 'http://swgclv.com', 'http://www.kromerradio.com', 'http://www.acmteam.com/acm/outside_home.asp', 'http://www.orvis.com/madison', 'https://www.retreataptsmcalpinecreek.com', None, 'http://www.elvischapel.com', 'http://www.ubreakifix.com/locations/peoria/', None, 'http://www.superchargefoods.com', 'http://www.thesakeexpress.com', None, 'http://www.topnoodle.ca', 'http://www.jazzberryteahouse.com', 'http://www.berkshireplaceapartments.com/', 'http://www.horizonhonorselementary.org', 'https://www.enterprise.com/en/car-rental/locations/us/pa/irwin-4021.html?mcid=iyp:8368400', 'http://www.4colorprint.com', 'https://deserttropicspools.com', 'http://martyscycle.com/', 'https://www.ttc.ca/Subway/Stations/Bay/station.jsp', 'http://www.sunsetgrill.ca', 'http://www.sothlv.com', 'http://www.palms.com/?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.ekgproperties.com', None, None, 'https://www.loandepot.com/branches/las-vegas-nv?sc_camp=DE925F8ECA0F4E0D8092C7E108A615A3', None, 'http://www.newmexicangrill.net', '1592161032', None, None, 'http://www.lenasflowersandgifts.com', 'http://www.cell2fix.com/queen-410-brampton/', None, 'http://www.tonymorenosalon.com', None, None, None, None, 'http://www.callister-law.com', 'http://www.smokeybones.com/', 'http://franklinPhotographyAz.com', '1592161065', 'http://www.thelastwordcharlotte.com/coffee-press', 'http://totalofficenc.com/', None, None, 'https://www.kaltire.com/en/stores/locations/?source=yelp_track&StoreID=864', 'http://www.corinthiapeoples.com', 'http://www.madurbanbees.com/', None, None, '1592161087', 'http://www.petopia.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.BarrowNeuro.org', '1592161101', 'http://www.southpittsburghvet.com', 'http://www.safeguardministorage.biz', 'http://www.lasvegasnvpoolservice.com', None, 'http://www.shopthepig.com', 'https://www.fatburger.com/locations/rancho', 'http://www.preferredparking.com', 'http://charkha.us/', 'http://www.hardboiledinc.com/', 'http://fasttowingaz.com', 'http://www.mephisto.com/us', None, 'https://locator.chase.com/oh/akron/50-s-main-st', 'http://www.lous.ca/', 'http://www.stratospherehotel.com/Food-Drink/Dining/Carvery-108', 'http://onestopnutrition.com', 'https://www.mimiscafe.com/locations/sunset-station/', 'http://www.nice1nails.com', None, '1592161151', None, 'http://diamondcarwash.ca', 'http://delucasplaceinthepark.com', None, 'https://www.torontobuffing.com', 'http://collinscleaners.com', None, 'http://xquiziteaffairz.com', None, 'https://locations.checkers.com/nv/las-vegas/4175-e-desert-inn-rd/?utm_source=Yelp', 'https://www.tedwiens.com', 'http://visionsource-southhills.com', 'http://www.timhortons.com/', 'http://www.arizonaeyedoc.com', None, 'http://www.mrhandyman.com/western-dane-county?sppccampaignid=67352&SPPC=Offline&L=true', 'https://www.whitbylibrary.ca', 'http://www.dangfinerentals.com', None, 'https://pizzariviera.com', 'http://eyetique.com', None, None, 'http://www.haulnassproductions.com/contactus.html', None, 'http://www.kinginklasvegas.com', 'http://www.hartwooddentists.com', 'https://www.ahwfac.com/', 'http://www.southparkoralsurgery.com/', 'http://store-locator.barnesandnoble.com/store/2039', 'http://www.imaginationchildcare.com', 'http://www.palazzo.com/entertainment/shows/baz.html', 'http://www.culturefreshlife.com', None, 'http://lvshotokan.com/', 'http://woolfeye.com', None, 'http://www.cloudadagents.com', 'http://www.viautorepair.info/', None, None, 'http://www.littlecaesars.com', 'http://terros.info', None, 'https://ad.doubleclick.net/ddm/clk/434334113;236814625;y', None, None, 'https://campbellssweets.com/locations/campbells-sweets-factory-ohio-city/', None, 'http://charmeck.org/mecklenburg/county/ParkandRec/Greenways/PlannedGreenways/Pages/McDowellCreekGreenway.aspx', None, None, 'http://www.italianvillagepizza.com/store-locator.html', 'https://locations.jackinthebox.com/us/az/chandler/900-n-cooper-rd', 'http://www.coldstonecreamery.com', None, 'http://www.smileworkscalgary.com', None, 'http://www.bannerhealth.com/locations/phoenix/banner-physical-therapy-mcdowell?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', None, 'https://rosyeyebrowthreading.business.site', 'http://www.sushiichibanchampaign.com', 'http://www.suenosimports.com', 'https://www.wellsfargo.com', '1592161298', None, 'https://www.davey.com/eastpittsburgh?source=Yelp', 'https://www.aria.com/en/restaurants/aria-patisserie.html', 'http://www.dpdough.com', 'http://www.us.allsaints.com/', 'https://www.payless.com/stores-location/OH-PARMA-6259.html', None, None, None, 'https://www.chick-fil-a.com/scottsdale101', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://thenakedbbq.com', 'http://www.ensurco.ca', 'https://www.mattressfirm.com/stores/az/scottsdale/mattress-stores-scottsdale-az-85266-6664.html', 'http://www.tenthousandvillages.com', 'http://chatime.com', 'http://www.childcareproviderlasvegas.com', 'http://www.meckabc.com', 'http://storelocator.pepboys.com/pepboys/stores/pittsburgh/library_road_service_center/01425', 'http://www.obskincare.com', None, None, None, 'http://www.valleyacademy.com', 'https://www.freshlandflowers.ca/?srccode=yelp_track', 'https://www.saladmeister.com', 'http://yogalovepgh.com', 'http://www.countyofdane.com/lwrd/parks/lake_farm.aspx', 'https://silvertoncasino.com/dine/dining-in-las-vegas-on-a-budget/', 'http://lasilmosoptical.com', 'https://www.solasalonstudios.com/salon-professional/lainie-schmidt2', 'http://winghartburgers.com/', 'http://www.bobzip.com', 'http://absoluteautoservicelv.com', 'http://tacoskissiphoenix.lunchroomconstructor.website', 'http://www.adelaideclub.com', 'http://www.drrudisill.com', None, None, None, 'http://www.maxandermas.com/locations/333038', 'http://mariannasalterations.com', 'http://www.bossplow.com', 'http://www.liquordepot.ca/?utm_source=Yelp&utm_medium=Online_Listings&utm_content=Location&utm_campaign=LiquorDepot_AB_Q3_July_September_2017', 'http://www.assuranceexteriors.com', None, 'http://www.shell.com', None, 'http://www.table51.com', 'http://www.recreation.gov/recAreaDetails.do?contractCode=NRSO&recAreaId=7&contractCode=131', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.wildpcs.com', 'https://ad.doubleclick.net/ddm/clk/301028788;127996861;v#/Live%20Weekend%20Entertainment', None, 'http://www.reebokcrossfitlibertyvillage.com/', 'http://www.pittsburgh-serenity.com', 'http://www.torontopubliclibrary.ca/detail.jsp?Entt=RDMLIB014&R=LIB014', 'http://dogboneranch.com', 'http://www.cleanjuice.com', 'http://dilworthcoffee.com', 'http://www.rompdogs.com', 'https://www.haircp.com', '1592161456', 'https://www.surlatable.com/browse/storeLocator/storeHome.jsp?storeId=140', '1592161460', 'http://filigreebeds.com', 'http://www.colonyamerican.com/?utm_source=Yelp!%20Regional&utm_medium=Text%20Link&utm_campaign=Yelp!%20Charlotte', None, 'http://www.juicebaratlvac.com', 'https://canyoncreekrestaurant.ca/vaughan/', None, None, None, None, None, 'http://www.acehardware.com/store-details/09471', 'http://www.timhortons.com/', 'http://www.barrospizza.com', '1592161494', 'http://smokeworldtempe.com', 'http://www.bestdoggonebookkeeping.com', 'http://www.banfield.com/veterinarians/az/phoenix/pho?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://alphaomegafg.com/', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/north-toronto-eglington-yonge-c245.html?mcid=iyp:8368400', 'https://www.aqua-tots.com/surprise', 'http://www.kortmaninc.com', None, 'http://browsthreadingsalons.com', 'http://www.strideawayequestriancenter.com', 'http://www.mattressfirm.com/', None, None, None, 'http://www.saigonphocuisine.com', 'http://www.salvationoutdoor.com', 'http://us.christianlouboutin.com/us_en/', None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://edhardyshop.com', 'http://www.parkshairhaven.com', None, 'http://www.hautechixvegas.com', 'http://integrity.helpusell.com', 'https://www.avis.com/en/locations/us/nv/las-vegas/qn4', 'http://www.matabar.ca', 'http://www.vivaldisalonsuites.com', 'http://ritzfurnitureplanet.ca/', 'http://movingteamsix.com', None, None, 'http://www.ecocleaners.ca/', 'https://locations.wendys.com/united-states/oh/parma/6970-ridge-road', 'https://www.discounttire.com/store/az/mesa/s/1294?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://biltmorenailbar.com', '1592161583', None, None, 'http://rumerzpgh.com/', 'http://www.suite114.ca', 'http://www.myspace.com/giant45', None, None, 'https://www.homedepot.com/l/Peoria/AZ/Peoria/85345/453?cm_mmc=seo-yelp&', None, None, '1592161607', None, 'https://www.k9viplv.com', 'https://www.hockeyworld.com/index/page/store_details/store_id/10', 'http://www.peninsulaluggageonline.com', 'https://www.phoeniciangaragedoorandrepair.com', 'http://www.LuminosityWellnessCenter.com', None, 'http://www.easternpodiatry.com', 'http://www.peppersfreshmarket.com', 'http://www.tremontscoops.com', 'https://local.albertsons.com/az/mesa/2727-n-power-rd.html', None, 'http://moviescoop.com', 'http://waikikigoldsilver.com', 'http://applefactory.com', 'http://www.brustersicecream.com', 'http://bigjohnspizza.ca', None, None, '1592161649', None, 'http://www.bigboy.com/', 'https://www.bluemercury.com/?utm_source=2016-Yelp&utm_medium=social&utm_content=49&utm_campaign=general', '1592161660', 'http://www.heritageatdeervalley.com', 'http://www.cellaxys.com', 'https://ireh-salon.business.site', 'http://noblecleaners.vegas', 'http://www.tuesdaymorning.com', 'http://specsonbloor.ca', 'http://www.estheticsbycristina.ca/', 'http://www.silkmanlawfirm.com', 'http://hubcapannielasvegas.com', None, None, 'http://www.eastcalgaryregistry.com', 'http://local.firestonecompleteautocare.com/ohio/akron/1245-firestone-pkwy/?lw_cmp=IYP_YPC_MLP_2046', 'http://www.fallsicecream.com', 'http://www.revitasize.ca/', 'http://www.elitefitnesstrainingandcoaching.com/', None, None, 'http://www.atozmovinganddriving.com', None, None, None, 'http://www.lagravineseappraisals.com', 'http://www.custombuiltpizza.com/', 'http://www.jeanvegetariankitchen.ca', '1592161722', 'http://beautyinvegas.com', 'http://www.countyofdane.com/lwrd/parks/indian_lake.aspx', 'http://www.phillipscliniclv.com', 'https://www.mattressfirm.com/stores/oh/streetsboro/mattress-stores-streetsboro-oh-44241-7782.html', 'http://www.hollywoodtans.com', 'http://budget.com', 'http://www.saltcreekofficefurniture.com', 'http://www.happycampersdental.com', None, None, 'http://www.pizzanova.com/locations/mississauga.html', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://h1racing.com', 'http://pdqmechanicalllc.com', 'http://www.edenwellnessvibration.com', 'http://yardbusterslandscaping.com', None, None, 'http://www.uwhealth.org/locations/detail.jsp?locationId=254', None, None, 'https://www.backfithealth.com', None, 'http://microsoft.com/en-ca/store/locations/ab/calgary/chinook-centre/store-1053?pointit_retailsustain_sitelinks_Yelp', 'http://ruggedmoosedecor.com', None, 'http://simplekitchento.com', 'https://www.republicservices.com?utm_source=yelp.com&utm_medium=referral&utm_campaign=Yelp_Profile_Click&utm_term=gTepcuWPpm5jqrVjM0gwew', 'https://www.standardplumbing.com/locations/PE', 'https://local.fedex.com/az/phoenix/office-5048/', '1592163820', None, None, 'https://ollyshoes.ca/pages/yonge-street-store', 'http://www.waterfrontoronto.ca/explore_projects2/west_don_lands/don_river_park', 'http://www.biggamblesrummagesale.com', None, None, None, None, 'http://www.arizonabouncearound.com', 'http://lavidamassageballantynenc.com', None, 'http://adultmart.com?utm_source=yelp&utm_medium=social&utm_campaign=yelptest&utm_content=url', 'http://www.firewatercalgary.com/', 'https://www.hertz.com/rentacar/location/unitedstates/arizona/phoenix/PHXC04', 'http://www.sameatshops.ca', 'http://mywheelguylv.com', 'https://locations.theupsstore.com/az/tempe/1753-e-broadway?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.shopsteelcity.com', 'http://www.RiteRug.com', 'http://www.thegolfdome.com', 'http://hianddrycleveland.com', 'https://plan.dignitymemorial.com/yp/plan/?id=542949820&utm_source=yp.com&utm_campaign=ypm&utm_medium=display&utm_term=386&utm_content=mlp', 'http://www.eurogyro.com/', 'http://www.marriott.com/hotels/travel/cltfa-fairfield-inn-and-suites-charlotte-arrowood/', '1592163884', 'http://www.logojoy.com', 'https://locations.theupsstore.com/az/scottsdale/16211-n-scottsdale-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.donttreadonbeans.com', None, None, 'http://www.sleepcountry.ca/', 'http://allcountypet.com', 'http://glenmeadowsauto.mechanicnet.com', 'http://www.parloursalon.com', None, 'http://www.merchantoftennis.com/', 'http://www.neshoffscarpetcleaning.com', 'http://www.fortmcdowelladventures.com', 'http://www.psychicamandamarquez.com', 'http://www.tricountymg.com', 'https://www.alaschools.org/arizona/az-schools/gilbert-k-6', None, 'https://pastureandplenty.com', 'https://palacestation.sclv.com/Gaming/Bingo?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', None, 'http://www.cupidstoybox.com', None, 'http://thesanddollarlv.com', 'http://www.usysnv.net/page/show/110658-bettye-wilson-soccer-complex', 'http://www.themeadowsschool.org', None, 'https://www.esso.ca/en/gas-station/richmondhill-on-beavercreekesso-200302403', 'http://www.studiocsalonsaz.com/studio-c', 'http://www.clorebeauty.com', '1592163956', 'http://klimateking.com/', 'http://www.spinco.ca', 'http://infinitevapor.com', '1592163966', 'http://www.thebrewteabar.com', 'http://www.chopchopchinesekitchen.com', 'http://www.chilitos.ca', 'http://thewienerscirclelv.com/', 'http://www.hob-nobs.com/', 'http://www.legendaryhomeservice.com', 'http://DefiantPestControl.com', 'https://www.napoli.vegas', 'http://www.brunswickkidds.com', 'http://www.ctrca.com/', 'https://www.trekbikes.com/us/en_US/retail/madison_west/', 'http://www.streetsofnewyork.com', 'http://nbdmd.com/', 'http://phoenix.gov', 'http://www.azpodiatrists.com', 'http://www.larryscocktails.com', 'http://www.cookout.com', 'http://spandexcity.com', 'http://www.casalinochiropractic.com', None, 'http://www.samdaebbq.com', 'http://balancingpawsdogtraining.com', None, '1592164037', 'http://www.revivme.com/las-vegas?utm_source=yelp-org&utm_medium=webclicks', '1592164042', 'http://www.beelogicpestcontrol.com', 'http://www.creativestyleslv.com', None, 'http://Www.bellaskinsalon.com', 'https://www.chick-fil-a.com/rossparkmall', '1592164058', None, 'http://www.bluejadechinese.com', 'http://nswhobgyn.com', 'http://brewsters.ca/', '1592164073', 'http://www.luxebrides.vegas', None, None, 'http://paradisebakery.com', None, 'http://actoneyouththeater.org', 'http://www.cityofhenderson.com/henderson-happenings/facilities/overview-of-pools/pool-locations/whitney-ranch-indoor-pool', 'http://www.7-eleven.com/?yelp=29384', 'http://www.johnniewalkerrv.com/index.php', 'http://www.ColleenSellsAZ.com', None, None, 'https://www.haircutmengibsoniapa.com', 'https://www.payless.com/stores-location/IL-CHAMPAIGN-5067.html', '1592164114', 'https://www.cafetempeaz.com', None, None, 'http://www.bartongrouphomesearch.com', 'http://foleysac.com', 'http://www.foodandwineexpo.ca/sitepages/', None, None, '1592164141', None, 'http://www.jaginchystuff.com', 'http://www.tremontpointe.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282975319&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.qashtonbeauty.com', 'http://www.phoenixairport.hilton.com', 'http://www.sweetaffairsbakeshop.com', 'https://www.verizon.com/home/storelocator/pa/pittsburgh-15206/', '1592164167', None, 'http://local.firestonecompleteautocare.com/arizona/peoria/10661-n-84th-ave/?lw_cmp=IYP_YPC_MLP_11932', None, 'http://www.azcoolmotors.com', 'http://www.shoproka.com/web/', 'http://www.gostorageone.com/self_storage/North_Las_Vegas/zip_89084/storageone_self_storage/10487', 'https://www.anytimefitness.com/gyms/1820/Markham-ON-L6B-0P2/?utm_source=yelp&utm_medium=local', 'http://www.pinkpolishnailspa.com', None, None, 'http://www.boyacklawgroup.com', 'http://dekra.us/en/nevada/las-vegas-3209-n-rainbow-blvd/', 'http://www.goplaycanada.com', 'http://www.crispfoods.com', 'http://www.restechservices.net', 'http://www.polepositionraceway.com', '1592164211', None, 'http://geraldinetoronto.com/', 'http://www.bakerperformingarts.com', 'https://dutchbros.com/?utm_source=las-vegas&utm_medium=yelp&utm_campaign=website_las-vegas', None, None, None, 'https://tortillafeliz.com', 'http://www.charlotterecyclery.org', 'http://www.maxmoving.ca', None, 'http://www.daggerdiesel.ca', 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/beachwood-fhsc', None, 'http://www.cannonpharmacies.com', 'http://www.bettysonking.com/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.waffluv.com/find-us', 'http://www.dunkindonuts.com', 'http://www.ytr.com', 'http://www.scoopnswirl.com', 'http://www.piedmont-eyecare.com', 'http://www.thefoodconnectionlv.com', None, 'http://www.starbucks.com/', 'http://www.copperrestaurant.com', None, 'http://www.peachykleenlaundry.com', 'https://wildfire.sclv.com/Wildfires/Wildfire-Rancho?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://extremepita.com', None, 'http://www.axelmortgage.com', 'http://www.hobbylobby.com/StoreLocator/Search?Latitude=33.2774819&Longitude=-111.73165570000003&SearchOn=85297&SearchDistance=50', None, None, None, 'http://www.myerstar.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', '1592164296', 'http://www.sportclips.com/', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282975058&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, '1592164307', 'http://www.busterstransmission.com', 'http://www.the-alley.ca', 'http://www.mifamiliamexicanfood.com', 'http://Www.thebubblegumgallery.vpweb.com', None, None, 'http://www.lincolnlandexpress.com/index.php', 'http://www.kaiulanidetailing.com', 'http://restaurants.quiznos.com/oh/lorain/amherst-44053', 'http://www.angelscremationandburial.com/', None, None, None, 'http://www.luxepethotels.com', None, 'http://www.officedepot.com/storelocator/az/chandler/officemax-6515/?cm_mmc=GMB-_-6515-_-Website-_-NS', 'https://www.hughesfloorcovering.com/yelp-offer', 'http://www.pinesatcarolinaplace.com', None, None, 'http://www.charlotteobserver.com', None, 'http://www.tmdish.com', 'http://www.insideoutpatio.ca', 'http://www.firecreekcoffee.com', None, None, 'http://www.QuickKeyLocksmithLasVegas.com', 'http://www.loftea.ca', 'http://sandersonplumbinglv.com', None, 'http://www.sopra.ca', 'http://mylifelinemd.com/', 'http://EUsweets.com', 'https://vinoandcanvas.com', 'http://www.desertsunpeds.com', 'http://www.allstardiscountmuffler.com', '1592164392', None, None, 'http://www.pokerpalace.net/', 'http://www.pizzapros.ca', 'https://www.thebso.com/locations/on/toronto/beauty-supply-outlet-haircuts-11813.html', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_112', 'http://www.salstuscangrill.com/', 'http://www.arizonahikebikeboard.com', 'http://www.providentlawyers.com', None, 'http://www.unicarcollision.com', 'http://kickstandcharlotte.com/', 'http://www.american-self-storage.com/avondale', None, 'http://www.TopScottsdaleHomes.com', 'http://www.ssrealtylv.com', 'http://www.thelimited.com', None, 'http://www.shawarma-palace.com', 'http://www.picturepeople.com/default.aspx?PK=e3adeef4-54b4-43c6-990a-619531e6637b', 'http://www.linsseafoodbuffet.com', None, 'http://www.whichwich.com', 'http://redlinediagnosticsllcauto.com', 'https://www.walmart.com/store/5085/belmont-nc/whats-new', None, 'https://stores.whitehouseblackmarket.com/boutique/white-house-black-market-kierland-commons', 'http://www.theconcordcove.com/', None, 'http://thenailchamber.com', '1592164461', None, 'https://www.paradisegrapevine.com', 'http://www.chrispuhlmanflowersandgifts.com/?srccode=yelp_track', 'http://phbalancedpool.com', 'http://www.timhortons.com', 'http://petemac.com/gilbert/', 'https://millersalehouse.com/locations/henderson/?utm_source=Yelp&utm_campaign=Yelp', 'http://nailing.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://vehbrothers.com', None, None, None, 'http://www.noizeboyz.com', 'http://www.originalchimneys.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.blackhawkcc.com', 'http://www.dollargeneral.com', 'http://kingdom-restaurant.business.site', 'https://www.choicehotels.com/illinois/urbana/comfort-suites-hotels/il366/rates', None, 'http://www.sunburstmusic.com', 'http://torontoauto.autotrader.ca/contact-form.htm', 'http://www.thecleverkoi.com/', 'http://www.madcitypetclinic.com', 'http://www.tandori.ca', 'http://www.waitressworldllc.com', 'http://homeinsulationaz.com', 'http://www.woodworkersemporium.com', None, 'https://www.elnuevotaquito.com', None, None, 'http://luxenailsspaphoenix.com', 'http://www.masakosushibar.ca', 'http://www.pandawokscarborough.com', None, 'http://www.tacobell.com', None, 'https://www.sunbritedental.com', 'http://atticsalt.co', None, None, 'http://www.drfineberg.com', 'http://www.uscryotherapy.com/location/scottsdale-az/', 'http://www.sureshotbilliardsaz.com', 'http://uspizzasurpriseaz.com', 'https://www.statefarm.com/agent/US/NC/Charlotte/Jack-English-YKJTS2RZ000?cmpid=M8V7_BLM_0006', None, 'http://www.bedbathandbeyond.com', 'http://www.arizonaministers.com', 'http://www.usairways.com?c=maplisting_Yelp_21041', 'http://www.arbys.com', 'http://www.kuohua.com', 'https://brighthomeenergy.com', None, 'https://www.meineke.com/locations/pa/monroeville-512/?utm_source=yelp&utm_medium=xvc', None, '1592164595', None, '1592164600', 'http://www.shoelessjoes.ca', 'http://azsportsmedicine.com', 'http://www.decadentdesserts.ca', '1592164609', 'http://www.whynotpizzaclt.com', None, 'http://www.diventures.com', 'http://www.ncix.com/', '1592164621', None, None, None, None, 'http://locations.michaels.com/oh/avon/1532/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.allamericanmodernsportsgrill.com', 'https://www.windsorstore.com/blogs/store-locator/az-scottsdale-scottsdale-fashion-square', 'http://www.trumphotels.com/las-vegas', 'http://www.grldcheese.com', 'http://www.wowwash.com', 'http://www.zoyogurt.com/arcadia/', 'https://hatfieldmedicalgroup.com/red-mountain-primary-care-arizona/', None, 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=669', None, 'http://shop.tuesdaymorning.com/', 'https://www.pizzaville.ca/stores/view/4335-bloor-street-w', 'https://www.meijer.com/shop/en/store/146/?cmpid=OLA:040319:YelpGrocery', None, 'http://local.skechers.com/AZ/GILBERT/237/', None, 'http://www.arbys.com', None, None, 'http://www.gratefulgardens.net', 'http://www.wynnlasvegas.com/Shows', 'http://www.recess.net/', 'https://www.aaautocarelv.com/locations/decatur-blvd/', 'http://www.remnanthealth.com', 'http://computerdocnc.com', None, None, 'http://www.papajohns.com', 'https://bananarepublic.gap.com', 'https://www.boehmerheating.com', 'http://fancynailsnorthlasvegas.com', 'https://www.vibenailbarlv.com', None, 'http://www.littlemountaincc.com', None, 'http://azglaucomaspecialists.com/our-locations/phoenix/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://icedoutbarbershop.com', 'http://www.moxies.ca', 'http://www.villamadina.com', 'https://www.davidyurman.com/stores/s/david-yurman-the-forum-shops-at-caesars?ecid=listing%20marketing%20store%20LasVegas%20all%20082216%20all', 'http://www.coconutsaz.com', 'http://www.superstarcarwashaz.com', None, 'http://naildistribution.com/', 'http://www.bk.com', 'http://www.screenlounge.ca/', 'http://beachpizzavegas.com/', 'http://www.anthropologie.com', 'http://www.comicheaven.com', 'http://www.quiktrip.com', 'http://richardsandoval.com/commissary', 'http://www.coldstonecreamery.com/stores/20030', None, 'http://lvbraces.com', 'http://www.silverspoonphoenix.com', 'http://www.ashleyfreehan.com', 'https://radiantdivine.com', 'http://www.dahmensathawks.com', 'http://www.kidsu.ca/', 'https://culinaryhc.com', None, None, 'http://www.luckybreakaz.com', 'http://www.3dudesquilting.com', 'http://www.theprincessmargaret.ca/en/pages/default.aspx', None, None, 'http://www.estrellamountain.edu/', 'http://www.greendrycleaning.ca', 'http://www.westshorehome.com', 'http://www.greatclips.com', None, 'http://laurel-md.yellowusa.com/', 'http://www.honestjohnspgh.com', None, 'http://www.tandoorichaska.com', 'https://www.tempemoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://myporcellis.com', None, 'http://www.JimmyJohns.com', None, 'https://www.godsgardentreasures.com', None, None, 'http://www.burns-scalo.com', 'http://www.mrsteamcarwash.ca', None, 'http://www.nouvellemariaspa.com/', 'http://rinckerlaw.com', 'http://www.drchemdry.com', 'http://nationsfreshfoods.ca', 'https://www.kohls.com/stores/nv/lasvegas-1372.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.fourpeaksrentals.com', 'http://www.canuckamusements.com', 'https://greenvalleyranch.sclv.com/Dining/Hanks?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://stores.sportsauthority.com/az/phoenix/sporting-goods-phoenix-692.html', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZGS', 'https://stores.bestbuy.com/nv/las-vegas/6950-arroyo-crossing-pkwy-1044.html/?loc=ns100&ref=NS', '1592164907', 'http://www.roccuzzorealty.com', 'http://www.surprisechildcare.com', 'http://www.shuttlersuniform.com', None, 'http://www.ecochoicewindows.ca', 'http://www.sushiandrolls.ca', None, 'http://www.backofhouse.ca/', 'http://www.handmunlimited.com', None, None, 'http://www.asimpleaffairlv.com', 'http://www.kegsteakhouse.com/en/locations/ON/toronto/mansion-keg/', 'http://www.spinellikia.com', 'http://www.saborcharlotte.com', 'http://www.kctowinginc.net/', 'https://www.crudowine.com', 'https://www1.shoppersdrugmart.ca', 'http://www.jaipurgrill.com', None, 'http://madisoneyecare.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.blackbearcharlotte.com/', 'http://mycupoftea.ca', '1592164974', None, 'http://olympiclimoservice.ca', 'http://www.beddingtons.com', 'http://villagecp.com', None, None, 'http://www.aonefingerprinting.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.66054.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:66054', 'http://elementsdrycleaner.com/', 'http://www.hungfooktong.ca', 'http://www.ayscater.com', '1592165005', None, 'http://www.mwuclinics.com', None, None, 'http://amelia-c.com/', 'https://www.hilton.com/en/hotels/pitmcht-home2-suites-pittsburgh-mccandless-pa/?SEO_id=YELP-HT-PITMCHT', 'http://www.dunkindonuts.com', 'http://local.buckle.com/PA/PITTSBURGH/415/', 'http://www.pleasantlakeapartments.com', 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', '1592165031', 'http://www.ateamair.net', 'http://GoldenRuleFB.com', 'https://locations.jackinthebox.com/us/nv/boulder-city/1101-nevada-hwy', None, 'http://www.greengardenflowers.ca/', None, 'http://local.skechers.com/AZ/GILBERT/237/', None, None, 'http://www.bestbuy.com', 'http://www.drshalupal.com/about.html', 'http://www.downwarddoggrooming.ca', None, 'http://www.exxonmobilstations.com/home.php?c=20140424134755&lang=en-us&storenum=757cfd0e77ee7a4ea34c6a6a556f7058', 'https://www.staples.com', 'http://www.federicosmexicanfood.com/', 'http://www.rainbowchiropracticcenter.com', 'http://www.janefendelman.com', None, 'https://glendaleparts.com', None, '1592165090', 'http://www.hairhappiness.com/ca/index.php', None, 'https://www.walmart.com/store/2112/scottsdale-az/details', 'https://www.druryhotels.com/locations/pittsburgh-pa/drury-plaza-hotel-pittsburgh-downtown', 'https://sincityent.com', 'http://www.bondplace.ca', 'https://allyouneedsmokeshop.com', 'http://www.suntechnc.com', 'http://www.mariepain.com', 'http://lazarbakery.ca', 'http://www.dollargeneral.com', 'http://www.platinumblondestudios.com', None, 'http://Chandlersmilesbrighter.com', None, 'http://www.meritagehomes.com/', None, '1592165136', 'http://fiveguys.com', None, None, None, 'http://www.barbarycoastcasino.com', 'http://abcsanitary.com', 'http://meatmarketvintage.com/', None, 'http://coconutcleaningco.com', None, 'http://bostonmarket.com', 'http://drlaffa.com', 'http://www.davescosmicsubs.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=723&utm_content=bpas', 'http://www.lrlv.com', None, None, 'http://www.bluediamondairductcleaning.com', 'http://www.castelloristorante.com', 'http://bit.ly/103bJzP', 'http://www.usps.com', 'http://aromawcs.ca', 'http://lifeguardsolutionsllc.com', None, 'http://www.chandlermall.com', None, 'http://www.aceretailer.com/aceonwilly/', 'https://reliancehomecomfort.com/toronto/', None, 'http://pizza.dominos.ca/Mississauga-Ontario-10348', None, 'https://www.clearchoice.com/locations/dental-implants-phoenix/?trans_id=webdisyelp&utm_campaign=Yelp&utm_source=YelpListing&utm_medium=Listing', 'http://www.4BCafe.com', 'http://www.onabun.ca', 'https://roxybar.ca', 'http://watchoutaz.com', '1592165236', 'http://www.drglick.com', 'http://licecrew.com', 'http://www.cafecentralclt.com', 'https://www.thebrick.com/pages/store-calgary-sunridge', '1592165249', None, 'http://wolfgangpuck.com/restaurants/casual-dining/wolfgang-puck-express/7730', '1592165258', 'https://www.dsw.ca/en/ca/', 'http://www.studio223az.com', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.andoverwoodsapts.com/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.7-eleven.com/?yelp=29384', 'http://www.evelinecharles.com/', 'http://www.bffgyms.com', 'http://bbdrybar.com/', 'https://stores.advanceautoparts.com/nc/charlotte/2910-freedom-drive?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', None, 'http://drakids.com', 'http://Www.lasvegaspsychic.com', 'https://www.vegasdeserttours.com', 'https://www.lasikvisioninstitute.com/lasik-eye-surgery/tempe-surgeon-center/?subid=TMP&venid=YLP31', 'http://www.7-eleven.com/?yelp=29384', 'http://www.la-mestiza.com/', None, None, 'http://check-please-cafe.business.site', 'http://www.sweetitis.net', 'http://www.papyrusonline.com/', 'http://cutenailscharlotte.com', 'http://www.drumsnflats.com', 'https://www.uhaaz.com', 'http://www.butlerplaza.net', 'http://www.filibertos.com', None, None, 'http://nynbeauty.com/', 'http://www.tastebudsyogurt.com', '1592165348', 'http://pellathehandyman.webs.com/', 'http://www.azmediquip.com', 'http://www.efilenevada.com/', 'https://himali-kitchen.business.site', None, 'https://gynecarelv.com', None, 'http://www.annschophouse.com', 'http://www.fitnessinmotionlv.com', 'http://wwwtowingwithtlc.wixsite.com/website', 'https://repestservices.com', 'https://www.ulta.com/stores/charlotte-nc-590', None, 'https://local.safeway.com/safeway/az/chandler/4970-s-alma-school-rd.html', 'http://www.dogsbollockspub.com', 'http://www.freshii.com', 'http://www.havencraft.org', 'http://www.ampm.com', 'http://www.rockyrivervineyards.com', 'http://www.gleemhomecleaning.com', 'http://www.peets.com/?cm_mmc=yelp*peets*8_28_12_homepage*na', None, 'http://www.aubreyshouseofroots.com', 'https://steakfrites.ca/fr/restaurants/detail/saint-sauveur/', 'http://www.theartshoppe.com', None, 'https://www.twiceasnicefood.com', 'http://motorlessmotionbicycles.com', 'http://www.bathandbodyworks.com', 'http://www.tayloredphotomemories.com', 'https://www.moes.com/find-a-moes/ohio/mentor/6467?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://bk.com/', 'http://www.marriott.com/hotels/travel/cltsd-springhill-suites-charlotte-uptown/', 'http://www.a1carlinemuffler.ca', None, 'http://www.sharpmyknife.com', None, 'https://www.arizonapartybike.com/scottsdale/', 'http://bradyhendersoninspections.com/', 'https://www.jamba.com/nc/charlotte/charlotte-douglas-int-l-airport-613', None, None, 'https://www.take5oilchange.com/locations/oh/bedfordheights-121/', 'http://www.ullaeyewear.com', None, 'http://www.lunaacupunctureaz.com', 'http://dignityvethospital.com', 'http://bodywaxinglasvegas.com', None, 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpwestorganic', 'http://www.legermainhotels.com/en/torontomls/', 'http://www.realcoolhvac.com/', 'http://www.meckafitness.com', 'http://vitalitybowls.com/locations/las-vegas/', 'http://www.southtrailhyundai.com', None, 'http://www.midas.com/pittsburgh/store.aspx?shopnum=6365&dmanum=688', 'http://www.ttc.ca', 'http://grainger.com/', 'http://www.thelakeshorespa.com', None, None, 'http://www.laurentianlanes.com', 'http://www.Park2300.com', 'https://classicwaterheaters.com', None, None, 'http://carpetcleanertoronto.ca', 'http://www.charlesalexanderdistribution.com', 'https://www.planetfitness.com/gyms/monroe-nc?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.thnclinic.com', 'http://www.rosenails.ca', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'http://www.jetluxuryresorts.com', 'http://www.arwright.ca', 'http://www.tugawaytowing.com/home.html', 'https://www.ttc.ca/Subway/Stations/Ossington/station.jsp#Schedule_', 'https://tempestoysterbar.com', None, 'http://www.locksmithsmadison.com', 'http://spicensabzi.us', 'http://www.moviesoncentral.com', 'http://www.jamisymonssalon.com/', None, 'http://locations.harristeeter.com/nc/charlotte/205/', None, 'http://www.saloncercone.com', None, 'http://eggsquis.com/fr/restaurants.php?restaurant=lasalle', 'https://www.montecarlo.com/en/restaurants/brand-steakhouse.html', None, None, None, 'http://www.carwashcleveland.com', 'http://sophiainsapphire.com', 'http://russospizza.net/', 'http://www.secondcup.com', 'http://edeninlove.com', 'http://www.rogersrepairservice.com/', 'http://doubletopping.com', 'http://www.charlotteautogroup.com', None, 'http://www.rebelbook.com', 'https://www.anylabtestnow.com/franchises/huntersville-28078', 'http://www.eatnpark.com', 'http://www.doubledoorinn.com', 'http://robertostacoshop.com', 'http://www.spirithalloween.com', 'http://www.marriott.com/hotels/hotel-rooms/yyzmd-courtyard-toronto-mississauga-west/', 'http://www.dunkindonuts.com', 'http://clevelandsteamercleaner.com', None, 'http://oaklandhallinn.com/', 'http://www.starbucks.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.startrekexp.com', None, 'http://us60selfstorage.com', None, None, 'http://www.jensontotalservices.com', 'https://www.olivegarden.com/locations/nv/las-vegas/las-vegas-cheyenne-ave/1363?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:las-vegas-nv-1363_pl:locurl_rd:1274', '1592165677', 'http://305kustomzdesigns.com', 'http://www.arthurmurrayscottsdale.com/', '1592165689', None, 'http://southwestsmilesdental.com/', 'http://www.prestigemusicacademy.com', None, None, None, None, 'https://www.wontonking.com', None, 'http://www.dunkindonuts.com', None, None, 'http://www.notecollection.com', None, None, 'http://rajafoods.ca', 'http://www.phoenixalterations.com', None, 'http://www.insurewithmelissa.com?cmpid=d3u7_blm_0006', 'http://www.cafe-mirage.com', 'http://livingyogacenter.net/', 'http://deserttintlasvegas.com', 'http://www.restoreandreplenish.com', 'http://www.palaciosupholstery.com', 'http://elisabat.com/', 'http://www.yogurttimedt.com', 'http://cityproperty.com', 'http://www.Ricosacai.com', 'http://www.alternativepaths.org', 'http://deerfootmeadowsoptometry.com/seton-optometry-location-and-hours/', None, 'https://thefaceshop.ca/en/pacific-mall-center-32-32-32-32/', 'http://www.silverminesubs.com/', 'http://seasaltbar.com', None, None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, 'http://www.menchies.com/frozen-yogurt-shops/frozen-yogurt--northland-plaza-ab', 'http://www.fosdalbakery.com', 'http://www.BombHairVegas.com', '1592165799', None, '1592165804', None, 'http://www.justroughinit.com', None, 'https://www.hazukiphotography.com', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://style-encorenorthhills.com', 'http://matchacafemaikoclt.com', 'http://Hydra-tattoo.com', 'http://www.sunautoservice.com/auto-repair/nv/las-vegas/las-vegas-tropicana-52', None, 'http://www.chura-hair.com', 'http://www.spoiledchics.com', 'http://www.docwalters.com', 'http://www.sushionbloor.com/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.litehouse.com', '1592165859', 'http://www.specializedflooringaz.com/', None, None, None, 'http://www.crywolfclothing.com', 'http://www.disantoimmigrationlaw.com', None, 'http://www.rossstores.com', 'http://www.popuppizzalv.com', 'http://www.thomaseyecare.org', None, 'https://budgetblinds.com/DowntownPittsburgh/?utm_source=yelp&utm_medium=naf-listing&utm_campaign=NAF-LOCAL-YELP', None, 'https://www.hankinsplasticsurgery.com', None, None, None, 'http://www.spirithalloween.com', 'http://www.heersmanagement.com/properties/property/desert-point-apartments', 'https://www.hilton.com/en/hotels/cltephf-hilton-charlotte-executive-park/?SEO_id=YELP-HI-CLTEPHF', 'https://www.foodandthingsliquoranddeli.com', 'https://www.hairclub.com/locations/on/toronto/hair-loss-clinic-242/?pub=loclisting&utm_source=yext&utm_medium=loclisting&utm_campaign=YX_242', 'http://tubbystubs.com', None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.dipsidoo.com', 'https://www.annaksalon.com', 'https://www.republicservices.com?utm_source=yelp.com&utm_medium=referral&utm_campaign=Yelp_Profile_Click&utm_term=a7viRDrdChmaTJUqBxg4EQ', 'http://www.urbanairgoodyear.com', 'http://ajsalterations.com', 'http://www.nevadacleanup.com', 'http://qdoba.com', 'http://www.purplepenguinsnow.com/', 'https://www.vietbeautysupply.com', 'http://www.nashvillenorth.ca/', None, None, None, 'http://www.lauerrealtygroup.com', 'http://tpmlasvegas.com', 'http://www.clerebar.com', None, None, None, 'https://www.elizabethtatelaw.com', 'http://www.elegancehaircare.com', None, None, 'http://yourspacesalons.ca/tonyc', 'http://www.greatclips.com/salons/3065', None, 'http://www.cherokeehillsgolf.com/restaurant', 'http://www.housetohomeinspection.com/', 'http://prairiefirechampaign.com/', None, None, 'http://cervantesrestaurant.com/', 'https://www.doanrestoration.com', 'http://www.tjbakerconst.com', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.lasvegasartificialgrass.com/', None, None, '1592166030', None, None, 'http://www.sonobello.com/locations/cleveland/?utm_source=yelp&utm_medium=site&utm_campaign=yelp_loc_page_url', None, None, None, None, None, 'https://www.kitchenstuffplus.com/storelocator/#kspST020', 'http://punjabibynature.ca/home.html', 'https://www.charlottefoot.com', '1592166055', 'http://www.kentlanes.com', 'http://www.pghtacotruck.com', 'http://www.tiltonlmt.wixsite.com/mysite', 'http://www.ghadirmeatmarket.com', 'http://www.starbucks.com/store/15887/', 'http://www.pizzanova.com', None, 'http://actionjacksfurniture.com/', 'http://taylorandcolt.com/commerce-court-toronto/', None, 'http://www.blindstogo.com/en/stores/east-mississauga?ua=L4X+1M1&rds=25', '1592166085', 'http://www.menchies.ca/frozen-yogurt-shops/frozen-yogurt-creekside-crossing-ab', 'https://www.searshomeservices.com/locations/appliance-repair/nv-las-vegas/4000-meadows-lane', 'http://www.sundeviltrophy.com/', None, '1592166100', 'http://www.lakeshorepediatric.com', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.popularlube.ca', 'https://www.southhillspetresort.net', None, 'http://www.plumbperformingartscenter.com/', 'https://www.vaqueroscarneasada.com', 'http://www.giantlasvegas.com', None, 'http://www.richsrestaurant.com/', 'https://riosecco.com', None, None, 'https://www.ritasfranchises.com/Brodheadsville', 'http://www.drivingtoindependence.com/', 'http://www.piazzamanna.com', 'http://www.lcbo.com', 'http://www.wxdx.com/main.html', 'http://thebelsize.pub', 'http://www.bannerhealth.com/locations/gilbert/banner-physical-therapy-gateway?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', 'http://www.caromonthealth.org/Locations/Hospitals/CaroMont-Regional-Medical-Center.aspx', 'http://tigerlily.com', 'https://www.mielesitalian.com', None, 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', None, 'http://www.peaceofmindandbodymassage.com', 'https://www.eatnpark.com', 'http://scarletdoorcafe.com', 'https://stores.maccosmetics.com/us/nv/las-vegas/3200-s-las-vegas-blvd', 'http://www.dominos.com', 'http://www.vinylwraptoronto.com', 'http://www.brillorestoration.com', None, 'http://www.dunkindonuts.com', None, '1592166203', 'https://www.ediblearrangements.com', 'http://www.ecosmartpros.com/', 'http://www.accurateautoglass.net', 'http://jennysalterations.wordpress.com/', 'http://www.whiskersandpawsvet.com', 'http://happyfeetnailsspa.com', 'http://www.stonefamilyservices.com', None, 'http://www.animalhospitalatgrayhawk.com', 'http://www.restaurantsawadee.com/', 'http://toronto.thepint.ca', None, 'http://cutie-giftshop.business.site', 'http://signaturebarbershop.net', 'http://cuyahogalibrary.org/', 'https://www.wellsfargo.com', None, None, 'http://mrniceguygames.wpengine.com/contact-us/', 'http://www.dunkindonuts.com', 'http://fiveguys.com/', 'http://www.papajohns.com/', None, 'http://www.sonicdrivein.com/', 'http://602autosports.com/', 'http://www.salonescapeaz.com', 'http://www.rocklobster.com.php53-12.ord1-1.websitetestlink.com/ossington/', 'https://www.4wheelparts.com/stores/north-carolina/4wp-charlotte-nc-54', 'https://www.petsmart.com/stores/us/az/phoenix-store0131.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.daango.com', 'http://restaurantspago.com', None, None, 'https://www.amr.net/home/lasvegas', 'http://www.hennashoppe.com', None, 'http://www.lickshomeburgers.com', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'https://www.pizza73.com', 'http://www.cigna.com/cmgaz/locations/stapley-multi-specialty-center', 'http://tempeimportsaz.com', 'http://www.restaurant-divino.com/accueil', None, 'http://www.big5sportinggoods.com', None, 'http://www.idoupdolasvegas.com', 'http://www.westlibertyanimalhospital.com', None, None, 'http://www.anteloelectric.com', 'http://www.happyhomeservicesaz.com', 'https://www.upmc.com/locations/community/south-side', None, None, 'http://www.newhighend.com', None, 'http://www.Visionworks.com', 'http://patio-pleasures.com/', None, 'https://www.unlv.edu/donnabeamgallery', 'http://www.virtualworldmadison.com', 'https://www.autozone.com/locations/az/phoenix/3908-e-thomas-rd.html', None, None, 'http://desertwestobgyn.com', 'https://www.twistedmindssmokeshop.com', 'http://www.PalmLane.ca', None, 'https://www.sportchek.ca', None, 'http://www.mezzaninehair.com', 'https://www.fatfreddyscatering.com', 'http://www.asepestandweedsupplies.com', 'https://www.ihg.com/holidayinnexpress/hotels/us/en/rantoul/cmirt/hoteldetail', None, None, 'http://www.babassupperclub.com', 'http://www.champagnestrands.com', 'http://www.boulevardvegas.com', '1592166417', 'http://bloomcigar.com', 'http://extensionroom.com', 'https://www.fascinations.net', 'http://www.theskullzsalon.com', None, 'http://www.indianpunjabibazaar.ca', 'https://www.bobevans.com/our-restaurants/locations/22?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', None, 'http://bestasianmassagelv.com', 'https://locations.davidstea.com/ab-calgary-111', 'http://www.papajohns.com', None, 'https://local.fedex.com/nv/las-vegas/office-1441/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEWI', 'http://www.vivintsmarthomesecuritycalgary.com', None, 'https://www.terravita.com/neighborhood', None, '1592166467', None, 'http://www.kelseys.ca/', 'http://ago.ca/ago-bistro', '1592166475', None, 'http://www.cbcautism.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'https://www.circlek.com/store-locator/us/tolleson/11450-w-southern/2701130', None, 'http://www.simpleaz.com', None, '1592166498', 'https://scottsdaleearnoseandthroat.com/about-us/meet-our-team/cheryl-a-mackechnie-md', '1592166505', 'http://www.lvcabs.com', None, 'https://hpautorepair.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXPC', 'https://www.purebarre.com/location/san-tan-village-az', 'http://www.canadapost.ca/cpotools/apps/fpo/personal/findPostOfficeDetailPrint?outletId=0000104239', 'http://www.onlinetickets.com/', 'http://www.cwpress.com/', 'http://thesaucebse.com', 'http://www.caferio.com/', None, None, 'http://www.heldtlumber.com', '1592166545', 'https://www.afw.com/stores/az/glendale', 'http://www.tenniswerx.com', 'https://www.publicstorage.com/north-carolina/self-storage-waxhaw-nc/28173-self-storage/2073?pid=wyelp&CID=1245&CHID=AFL', 'https://www.autozone.com/locations/az/phoenix/3908-e-thomas-rd.html', 'http://www.purcelltire.com/retail/retail-locations.aspx?store=85', None, None, 'http://www.envynailspaclt.com', None, 'http://www.organicgarage.com', 'http://abbottcourtesyplumbing.com', None, 'http://www.americanrealtylv.com', 'http://www.angelosohio.com/', 'http://www.sipcoffeeandbeer.com', None, 'http://www.osteriausa.com', None, 'http://www.homegoods.com', 'http://www.vegas-asian-massage.com/', 'http://www.cristinahindslaw.com/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.shangrilabanquet.com', 'http://japanesespecialties.blog.fc2.com/', 'http://www.gordonbiersch.com', 'http://www.awildhairaz.com', 'http://www.switchbladesalon.com', 'https://www.dairyqueen.com/us-en/locator/Detail/?store-id=5175&localechange=1', 'http://www.theloreleiboutique.com', 'http://www.chandleraz.gov/tumbleweed', 'http://www.pizzahut.com/', None, 'http://www.harrisonlawaz.com', 'https://www.menswearhouse.com/store-locator/2513?utm_source=yelp&utm_medium=listing&utm_content=2513&utm_campaign=AZ', 'http://palacenaillounge.net', None, 'http://www.falconlandscapes.com', 'http://www.trueharmonywellness.com', 'http://lodgecharlotte.com', None, 'http://www.moonflightcoffee.com', 'http://subamanautocare.com', 'http://www.theotheroomlv.com', None, None, 'https://tannertileandstone.com', 'http://rebathandkitchens.com', 'https://www.target.com/sl/mccandless/1218', None, 'https://jamboree-bagel.business.site', None, None, 'https://www.arrowheadccaz.com', None, 'http://floydsbarbershop.net/', 'http://www.livemagnoliaterrace.com', None, 'http://www.oasisspasalon.com', 'https://www.homedepot.com/l/Bethel-Park/PA/Bethel-Park/15102/4176?cm_mmc=seo-yelp&', 'http://www.platosclosetcuyahogafalls.com', 'http://www.quesada.ca', 'http://www.sdsdental.com', 'http://www.ipdiet.com', 'http://www.NEwomensclinic.com', None, None, None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280216620&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.customcarconcepts.net', None, 'http://www.fabricboutique.com/', 'http://stores.save-a-lot.com/crafton-pa', None, 'http://www.acu-painclinic.com/index.html', 'https://mollymaid.com/southwestern-charlotte-fort-mill-rock-hill', None, 'http://99only.com/store/Mesa---Main/', 'http://www.regaleaz.com/', 'http://www.centennialcollege.ca', 'http://www.carinobistro.ca', 'https://www.ridgeatrobinson.com', 'https://www.integramedical.com', 'https://local.fedex.com/oh/fairlawn/office-1229/', 'http://www.timhortons.com/', 'http://www.graftmadison.com/', 'http://www.arcadiafamilyclinic.com', 'http://www.bayequityhomeloans.com/gilbert', None, None, None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=12197&localechange=1', None, 'http://www.islandpethospital.com', None, None, 'http://www.marshallscanada.ca', 'http://www.tzatziki.ca', None, 'https://www.thejoint.com/arizona/mesa/red-mountain-48026', 'http://www.callcoolaid.com/', None, 'http://www.hoerner.ca', 'http://www.greatlakesoutdoorsupply.com', 'http://www.thefatbelgian.com/', 'http://thailandspamassage.com', None, 'http://www.surgicalweightcontrolcenter.com', None, 'http://www.sonoranorthotrauma.com', None, None, 'http://www.vcahospitals.com/elliot-park/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Elliot_Park_Animal_Hospital&utm_campaign=main_url', 'http://www.eyebrowsrus.com', 'http://www.herriotts.com', 'http://www.longsontherapy.com', None, None, 'http://www.ardene.com', None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.dominicspizzamedina.com', 'http://atrautoglass.com', None, 'http://livingwellhomes.com/apartments/details/escondido_apartments', 'http://www.swisschalet.com', 'http://justincookhomes.com', 'http://octanecf.com/', 'http://www.theladysilvia.com/', 'http://www.whitfillnursery.com/', None, None, 'http://theodorewilliamslaw.com/', 'https://upscalemixologist.com', None, 'http://fancynailsaz.com', 'http://www.vivalasguestlist.com', 'http://www.dwr.com/category/find+a+studio/scottsdale.do?mobile=off', None, 'http://gilbert.donutworryaz.com', 'http://greenleafeinncharlotte.com', 'http://www.ahsappliance.com/', None, 'https://www.villageeastcleaners.com', None, None, 'http://info.lululemon.com/stores/us/las-vegas/fashionshowmall', 'http://www.involtini.ca/', 'http://www.blackforestbooksandtoys.com/', 'http://drjimshipley.com', None, 'http://www.arizonaorganic.com/', 'http://www.jasontheplumberllc.com', None, 'http://www.benfranklinplumbingcharlotte.com', 'http://www.aznypdpizza.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://Geostacos.com', 'https://www.thingsremembered.com', 'http://bikepirates.com/', 'http://manhattanpizza4lv.com', 'http://www.greatclips.com/salons/9261', None, 'http://www.divinedoggies.ca', 'http://www.desertdove.com', 'http://www.LocalMotionPGH.com', 'http://www.shopchristophertodd.com', 'http://www.umamipoke.com', '1592167022', 'http://www.marathon.com', 'http://www.timhortons.com/', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.premiercoachworks.com', None, 'http://swigs.ca', 'https://globalgifts.ca', None, 'http://www.sfxphx.org', None, 'https://www.napaonline.com', None, '1592167056', 'http://directpcc.com/', 'https://www.cricketwireless.com', 'http://www.gotaticket.net', None, None, None, 'http://www.rentalstempe.com', None, 'http://www.costco.ca/warehouse-locations/vaughan-woodbridge-on-547.html', 'http://www.momosushilasvegas.com', 'http://threeamigoscharlotte.com', 'http://www.sincitycomputerservices.com', 'https://www.petahead.ca', None, 'http://www.acropoliscg.com', 'https://www.interdent.com/gentle-dental/locations/az/phoenix/702-e-bell-rd-dentist-office/', 'http://www.foundery.is/', 'http://waxhawdentalcenter.com', 'http://www.trainwithgabe.com', 'http://laplanchagrills.com', None, 'http://eastwestblinds.com/?utm_source=Yelp&utm_medium=Yelp%20CPC&utm_campaign=Yelp%20East%20West%20Blinds', 'http://bespokeinn.com/', 'http://www.dunkindonuts.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.craigrd.com/', None, 'http://www.cash4chaos.com', None, None, 'https://www.autozone.com/locations/az/scottsdale/7401-e-mcdowell-rd.html', 'http://www.acebartending.com', 'https://www.target.com/sl/las-vegas-blue-diamond/2164', 'http://newbeginningscounselingcenters.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://stockmanos.com', None, None, 'http://www.blingtour.com', 'http://charlotteswim.com/', 'http://www.chiro-phoenix.com', None, 'http://alterios.webs.com/', 'http://azteccaraudio.com', 'http://www.arizonaveterinaryoncology.com', 'http://www.robertcoomergroup.com', None, 'http://www.portofsubs.com', 'http://gastondentalassociates.com/', 'http://www.aapglv.com', 'http://www.practiceofpositivity.com', 'https://hirehometeam.com', 'https://www.kohls.com/stores/nv/henderson-667.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.hillsideappliancerepair.com', 'http://www.lorain.lib.oh.us', 'http://www.dunkindonuts.com', None, 'http://www.Konbeasushi.com', 'https://www.walmart.com/store/1598/phoenix-az/whats-new', 'http://www.agaveyaguacate.blogspot.com/', 'http://www.periodentalimplant.com', 'http://www.nandos.ca/restaurants/calgary-17th-coming-soon', 'https://www.signaturestyle.com/locations/on/richmond-hill/first-choice-haircutters-51417.html', 'http://aproposcreations.com/', 'http://www.theshopprinting.com', 'http://fritesstreet.com/', 'http://www.cyanimalclinic.com', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', None, 'http://local.buckle.com/OH/WESTLAKE/419/?utm_source=Buckle&utm_medium=Website&utm_campaign=Store+Locator', None, 'http://www.starbucks.com/store/9334/', None, 'http://rebeltoronto.com', 'http://mikasgreek.com', None, 'http://www.premiumgranite.com', '1592167276', 'http://pouloslawfirm.com', None, None, None, 'https://andersondentalaz.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.devicepitstop.com', 'http://www.keungsrestaurant.com', None, 'https://www.chickasawdemolition.com', None, 'http://washmeohio.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://Lasajspa.com', 'http://transnationalmoving.com', None, 'http://www.pinkberry.com', 'http://www.paradiseflowermarket.net', None, None, 'http://spamontst-hilaire.com', 'http://www.aamco.com/centerinfo.asp?centerNum=4128569500', None, 'http://www.banfield.com/veterinarians/nc/cornelius/coe?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, None, 'http://www.wbt.com', 'http://tanakasmartialartslasvegas.com', None, 'http://www.arrowprofessionals.com', 'http://www.princetonclubxpress.net/', 'http://www.parkersdowntown.com', '1592167562', None, None, None, None, 'http://www.hibachigrillphoenix.com', None, 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', '1592167582', 'http://www.theartshoppe.com', 'http://www.stjohnsmusic.com/locations/calgary', None, None, None, 'http://www.spanishtrailcc.com', None, 'https://www.kruyerdental.com', None, 'http://www.fellinislv.com', '1592167611', 'http://sincitybrewtours.com', None, '1592167616', None, 'http://www.caseysdrafthouse.com', None, 'http://www.tradesecrets.ca/', None, 'http://otrocafe.com', 'http://www.lvnailspanv.com', 'http://www.letseat.at/paparazzipizzeria#home', None, None, 'http://lapaloma.ca/about-us/', '1592167648', 'http://www.healthyplanetcanada.com', None, None, None, 'https://www.aplaceformom.com/assisted-living/arizona/phoenix', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592167664', 'http://www.Kaizensushi.ca', None, 'http://helpinghandhandymanservice.com/handyman-services/', None, 'http://www.furniturebank.org', 'http://www.verizonwireless.com/', 'http://www.buddhabodyyoga.ca', None, None, None, 'https://www.rodiziogrill.com/henderson-nv/', 'http://www.sunridgemazda.com', None, 'http://www.breastforbaby.com', 'http://www.bowlingdynamics.com/', 'https://www.americanrealtyacademy.com', 'https://www.ashleycourt-apartments.com', None, 'http://www.lasvegashairandmakeup.com', None, None, 'http://www.campbowwow.com/summerlin', 'https://centennialhillsrealty.managebuilding.com/Resident/PublicPages/Home.aspx', 'https://www.anytimefitness.com/gyms/2194/Cottage-Grove-OR-97424/?utm_source=yelp&utm_medium=local', None, 'http://www.glickdental.com/', 'http://Lawdawgtrailtours.com', 'http://www.citymarketdeli.com', None, 'http://www.regalnails.com', 'http://www.tipitytoenails.com', 'https://www.foodforthought.ca/contact-us/markham', 'http://www.salonlola.net', None, None, 'https://www.publicstorage.com/arizona/self-storage-phoenix-az/85027-self-storage/1113?pid=wyelp&CID=1245&CHID=AFL', None, None, None, 'https://bridalxoxo.com', 'http://www.statewidelightinglasvegas.com', 'https://www.enterprise.com/en/car-rental/locations/us/oh/mentor-3921.html?mcid=iyp:8368400', 'http://www.cozinedental.com', 'http://www.lessermeansmore.com', 'http://www.drinkbambu.com', None, 'http://www.villaserenahenderson.com', None, '1592167790', 'http://www.sevencalgary.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.hilton.com/en/hotels/cltsohw-homewood-suites-charlotte-southpark/?SEO_id=YELP-HW-CLTSOHW', None, 'https://www.menswearhouse.com/store-locator/2503?utm_source=yelp&utm_medium=listing&utm_content=2503&utm_campaign=AZ', 'http://www.eastwestbank.com', 'https://stores.godiva.com/us/nv/las-vegas/3200-las-vegas-blvd-s.html', None, 'http://www.fracturedprune.com/location_charlotte.php', 'http://www.arizonapoolpros.com', 'http://www.kleinhenzjewelers.com', None, 'http://www.eastvalleypetdoors.com', 'http://www.chatpattachowk.ca', None, 'https://www.bostondentalgroup.com/locations/happy-dental-west-valley/', 'http://www.dasonii.com', 'http://gourmetschnitzelhouse.com/', 'https://www.kohls.com/stores/pa/monroeville-289.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.parasitetesting.com', 'http://www.picnicfood.ca', 'http://counseling.healingcouples.org', 'http://www.ssrtowing.com/', None, '1592167861', 'http://www.Vegasjj.com', 'http://www.jerianchiropractic.com', None, 'https://www.sprint.com/storefronts/bd/sprint-chandler-az-85226-fcs-1172/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.starbucks.com', 'http://fitnesstogether.com/waxhaw?utm_source=Yelp%20Web&utm_medium=Yelp%20Web&utm_campaign=Yelp%20Web', 'https://www.carefreecoverings.com/home', None, 'https://www.sunsetgrill.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://arizonareptilecenter.co/', 'http://www.tastidlite.com/', None, None, 'http://www.victoriassecret.com', 'http://www.arrowoodmed.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.indiascafeandkitchen.com', None, 'http://www.dollartree.com', 'http://www.soshandyman.ca', 'http://www.greencleanphoenix.com/', None, None, None, 'http://paninisgrill.com/locations/euclid', None, 'http://www.cellxperts.ca', 'http://www.mamarobertos.com', 'http://www.subaruofmaple.com/', '1592167950', 'http://www.aaronvargaphotography.com', 'http://modernvascular.com/modern-vascular-of-glendale/', None, '1592167966', 'http://www.yourserenity.ca', 'http://fiveguys.ca', 'http://www.eddiebauer.com', 'http://cosmonailsmesa.com', 'http://www.christieclinic.com', None, 'http://vacationownershipconsultants.com', 'http://www.mcdonalds.com', 'http://www.wardenandsons.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.affirmhartman.com', 'http://rdnplumbing.net', 'http://www.allegromusicaz.com', 'http://www.bevsbeadz.com', 'http://www.phatpackshow.com/', None, 'http://www.bdcdental.ca', 'http://www.sweetnote.ca', 'https://4tenrealestate.com', 'https://www.painteddesertgc.com', 'http://www.marinoswickliffe.com/', 'http://www.delimarkcafes.com/477mtpleasant.html', None, 'https://www.r2smile.com', 'http://www.yelp.com/events/charlotte-hops-and-shops-2', '1592168035', 'http://www.rentcoldair.com/', None, 'http://7keystohealthinc.com/contact-us/', None, 'http://www.massageaddict.ca/mississaugameadowvale', 'http://www.stripper101.com/', None, None, 'http://www.quiktrip.com', 'http://pageperpage.com', 'http://www.stephencooley.com', '1592168063', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB060&Entt=RDMLIB060', 'http://tradition.market', 'http://www.thepeacepipe.net', 'http://www.lasvegassuites.com/', None, None, None, '1592168082', 'https://locations.theupsstore.com/pa/pittsburgh/4885-mc-knight-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.hoopershealth.com', 'https://arizona.weidner.com/apartments/az/phoenix/roosevelt-row/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.centuryelectricllc.com', None, 'http://www.vieweyecare.com/', None, None, None, 'http://www.carusogourmetpizza.com/', 'https://locations.wendys.com/united-states/az/goodyear/1178-n-litchfield-rd', None, None, 'http://www.massimodutti.com/ca', 'http://www.restaurantrouge.com/', 'http://www.thesportspub.com/', 'http://www.ektaxandaccounting.com', 'https://locations.vitaminshoppe.com/az/scottsdale/vitamins-supplements-scottsdale-az-571.html', 'http://www.AgaveTreeAndLandscape.com', 'https://www.marks.com/en/stores/rexdale-etobicoke-55-woodbine-downs-blvd.html', None, 'https://www.thearrogantbutcher.com', 'http://www.adenearthworks.com', None, None, None, None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89084/600-in-north-las-vegas/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-600&utm_content=website-link&howheard=IYE', 'http://www.roserunkennel.com', 'https://www.thebso.com/locations/on/aurora/beauty-supply-outlet-haircuts-11847.html', 'http://www.allfireduplv.com', 'http://www.visitingangels.com/AZ', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'http://www.conns.com/store-locator/north-carolina/charlotte-28273', None, None, None, None, 'http://www.superstarcarwashaz.com/w_services2.php', 'http://www.goldstockjewelers.com', None, 'https://www.uhaul.com/Locations/Self-Storage-near-Litchfield-Park-AZ-85340/721037/', 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', None, 'http://eastvalleypulmonary.com', 'https://www.gucci.com/us/en/store/7014-east-camelback-road?utm_source=yelp_us&utm_medium=storemarketing&utm_campaign=retail_storepages_marcomm&utm_content=23016_bookapp', None, 'https://www.ritasice.com', None, 'http://www.joinrmxprofessionals.com', None, None, 'http://bartlegibson.com', 'http://www.progressivehome.com', 'http://www.elpolloloco.com/locations/store/3855', 'http://www.problindrepair.com', 'http://stacyneal.wvmbmesa.com', 'http://www.hyattcarcompany.com/', None, 'http://www.thebeehivegifts.com/', None, None, 'http://luckyboyburgershopphoenix.bestcafes.online', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Chandler-AZ-85226/922030/', '1592168214', 'http://jwmechanical.com', 'http://www.dogdaystempe.com', None, 'http://www.venetian.com', 'http://villageclubs.com', None, None, 'https://www.titlemax.com/store/phoenix-e-warner-az-41-title-loans/?utm_source=yelp&utm_medium=listing&utm_campaign=places&tmx_id=771c0159ac754cf&sf_traffic=paid_listing_yelp', 'https://risasdental.com/find-a-location/tempe/?utm_campaign=LocationPage&utm_medium=TempeYelpWebsite&utm_source=Yelp', 'https://www.robinsplumbing.com', None, 'http://www.kierlandcigars.doodlekit.com/', 'http://www.rtthomegroup.com', None, 'http://www.samifruits.com', None, 'http://www.zeppes.com', 'http://www.southshoresah.com', '1592168256', 'http://www.meetfreshcanada.com', 'http://www.chandlerfamilycare.com', 'http://www.dadanddaughterphotography.com', 'https://www.themattressmania.com', None, 'http://uberadventures.net', 'http://megatirecalgary.com', None, 'https://stayatthei.com', None, 'http://www.harborfreight.com', '1592168284', None, 'https://runpigrun.ca', None, 'http://pranamanana.com', 'http://www.isscogenerator.com/main/', None, 'http://www.runplusfun.com', '1592168301', 'http://www.bowlology.com', 'https://www.ulta.com/stores/henderson-nv-1191', 'http://chase.com', '1592168311', 'http://www.floorsforless.com', None, 'http://www.3030dundaswest.com', 'http://www.krankensigns.com/', 'http://www.laurellake.com', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'http://www.graceaz.com', 'https://www.roostersmgc.com/locations/nc/huntersville/torrence-village-haircuts-13194.html', 'http://www.greatclips.com/', 'http://omegamassage.ca/', None, 'http://www.wiler.org', None, 'http://azrattlers.com/', 'http://hawksgym.com', None, None, None, '1592168350', 'http://xaviermortimer.com', 'http://www.teejaysbrampton.com', 'http://leesliquorlv.com/locations/the-crane-bar', 'http://portofinocrs.com', 'http://www.mississauga.ca/', 'https://www.foresthillortho.com', None, 'http://my.clevelandclinic.org/departments/eye', '1592168367', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', None, 'http://www.bk.com', 'http://www.urbanhomeandgarden.com', 'http://N8tiveArts.com', 'https://www.publicstorage.com/south-carolina/self-storage-lake-wylie-sc/29710-self-storage/2566?pid=wyelp&CID=1245&CHID=AFL', 'http://www.valleyairworks.com', None, 'https://www.vagaro.com/nailsbyyulie', 'http://www.schaffers.com/', None, 'https://www.eaglerider.com/phoenix', None, 'https://www.SearsHomeServices.com/locations/appliance-repair/nv-henderson/1245-w-warm-springs-rd', 'https://www.wellsfargo.com', 'http://www.makeupbykyra.com', 'http://encorecatering.com/', 'http://www.cbdemporiumaz.com', '1592168410', 'http://pawntnt.com', 'http://baywoodclinic.com', None, None, 'http://www.corvobartoronto.com', 'http://www.spicersprinklerworks.com/', None, 'http://www.expertnailandspa.com', 'http://cleaningservicecharlotte.net', None, 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', None, None, None, 'https://www.pods.com/locations/united-states/nevada/las-vegas', 'http://www.blackmountainortho.com', 'https://advancedvisioninstitute.net', 'http://christophersfinedrycleaning.ca', None, 'http://www.canvasgallery.ca', 'http://browart23rosspark.com', None, 'https://local.safeway.com/safeway/az/phoenix/810-e-glendale-ave.html', 'http://www.epiclandscapelv.com', 'http://local.buckle.com/nv/las-vegas/457/', 'http://italianoasispizzeria.com', 'http://www.lmca.org/about/lmcafe.cfm', None, 'http://www.flutedmushroom.com', None, 'http://cleaningwonders.com', 'https://www.msisurfaces.com/phoenix-countertop-showroom-distribution/?utm_source=yelp&utm_medium=cpc&utm_campaign=yelp_monthly', 'http://www.memphisstationbar.com/', 'http://www.berdenas.com', 'http://www.tacobell.com', None, None, 'http://www.jacobsonbrosdeli.com/', 'http://www.dornellas.com/', None, 'http://www.bikebike.ca', None, 'http://www.beautybrowsalon.com', 'http://www.theupsstore.ca/60', 'http://www.azmistsystems.com', 'http://www.ajsspamillennium.com/', None, 'http://www.dsw.com', 'http://www.elitefamilydental.com', None, 'http://solita.ca', None, 'http://www.hugoboss.com', 'https://horsebacktrailriding.com', None, 'http://www.cpk.com/location/details/Chandler', None, 'http://www.salonlevel6.com', 'http://www.twainandswensonstorage.com', None, None, None, None, 'http://www.fanniemay.com/', 'http://tavernedelaferme.ca', None, None, 'http://www.essentialskinaz.com', 'http://www.newcreationssalon.com', 'https://www.nevadalegalforms.com', 'http://www.masterhardwarepa.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.theinnersleeve.com', '1592168571', 'http://www.serviceking.com/locations/service-king-falconis?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'https://cinemark.com/nevada/century-16-santa-fe-station-and-xd', 'http://www.metrogreenscape.com', 'http://mkautomotive.com', 'http://www.teuschertoronto.com', None, None, None, None, 'http://www.dininginaz.com', 'http://sc-clinic.com/clinic/spadina-and-bloor/', None, None, 'http://www.maxumconstruction.net', 'https://www.walmart.com/store/6586/concord-nc/whats-new', 'http://www.smartpointresearch.com', 'https://www.cfshops.com/toronto-eaton-centre.html', 'http://www.elmnt.ca', 'http://dubaijewellers.ca', 'http://www.pizzabreak.ca/', 'http://labahiaasadosymariscoslasvegas.cafesonly.online', None, None, None, None, '1592168629', 'http://www.precisiontune.com/ConcordNC', 'http://beyerapplianceservice.com', 'http://www.completemarine.com', 'https://www.food4less.com/', None, None, None, 'http://sundevilpool.com', '1592168649', 'https://www.handandstoneballantyne.com', 'https://blackbeardiner.com/location/glendale/', 'http://fastlanepizza.com', 'http://www.arizonasrealty.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, None, None, 'http://k9-games.com', None, 'http://www.carolinashealthcare.org/charlotte-medical-clinic', 'http://www.gmurrayphoto.com', 'http://stcharlesonline.org', 'http://www.classiccakesaz.com', 'http://www.tiptopautocollision.com', None, 'http://www.fresh-burger.com/', 'http://www.lakesidesportschiro.com', 'http://flobarlounge.com', None, None, 'http://www.fat-tuesday.com', 'http://www.stowintegrityauto.com', 'http://experiencetheblackout.com/', 'http://www.charlotteappliancerepairmen.com', None, '1592168709', 'http://www.redtailgolfclub.com', 'https://www.balancinghormonesnaturally.com', 'http://www.emb-plus.com', 'http://famouslaffa.com/', 'http://stores.sportsauthority.com/az/phoenix/sporting-goods-phoenix-692.html', 'https://cigarsdaily.com', 'http://www.centralphoenixanimalhospital.com', 'https://lvfamilyvision.com', None, 'http://www.cuttingedgecalgary.com', 'http://www.rentaffordable.com', 'http://www.sunnydayslearningcenter.com', 'http://www.oasisspringsbuilders.com', 'http://www.surf-ski.com/', 'http://www.kwakballet.com', 'http://www.setmefree.ca', 'http://cashcanada.com/pawn-shop-location/cash-canada-forest-lawn', 'http://universalenroll.dhs.gov', 'http://www.kfc.com', None, 'http://www.haircutie.com', 'http://www.mcdonalds.com', 'http://frugalmuse.com', None, 'https://www.snaderlawgroup.com', 'http://www.acehardware.com/store-details/15917', None, 'http://www.stlouiswings.com', 'https://www.abuelos.com/restaurants/chandler/', None, 'http://www.shenanigansbarandgrille.com', None, 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'https://www.anytimefitness.com/gyms/3912/Litchfield-Park-AZ-85340/?utm_source=yelp&utm_medium=local', None, 'http://wynnfitness.com/location/mississauga', None, 'http://newvisionpropertymanagement.com/', 'http://www.islanddentalcenter.com', 'http://www.hootersarizona.com', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', None, 'https://lernerandrowe.com/?utm_source=Yelp', None, 'http://www.murrayhillfoods.com', '1592168804', None, 'https://locations.panerabread.com/il/aurora/1304-fox-valley-center.html', 'http://Therapeuticretreat.Com/', 'http://www.instantbeautyspa.com', None, 'http://www.nest.to/', 'http://alexblackgolf.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.verizonwireless.com/stores/ohio/streetsboro/streetsboro-357953/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.dollarama.com', 'http://www.gustafsonlawoffice.com', 'https://www.core704.com', 'https://dealer.sprint.com/experts-choice', None, 'http://www.dragonscandy.com', None, 'http://www.suncitysummerlinflorist.com/?srccode=yelp_track', 'http://www.smoknpig.com/', 'http://www.rahrawrahpetfood.com', None, None, 'https://arizona.weidner.com/apartments/az/phoenix/trailside-at-hermosa-pointe-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'https://dentistryofthecarolinas.com/locations/monroe/', None, 'http://www.timothys.ca', 'https://www.nofrills.ca/store-locator/?utm_campaign=Loblaws&storeId=1384&utm_medium=LPM&utm_source=G', None, 'http://www.lu-az.com', 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', 'https://tahdesign.com', None, None, 'https://www.alphagraphics.com/centers/charlotte-north-carolina-us287.html', None, None, None, 'http://www.sabas.com', None, None, 'http://www.picknsave.com', 'http://locations.harristeeter.com/nc/harrisburg/92/', '1592168889', 'http://all-tranz.com', None, 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', 'http://thefrogandcrown.com', 'http://popeyeschicken.ca/', 'http://www.muchoburrito.com', 'http://www.starbucks.com/store/17296/', 'http://www.stratospherehotel.com/american_superstars.html', 'http://www.foodlion.com', None, 'https://www.walmart.com/store/3473/las-vegas-nv/whats-new', 'http://www.hayashihibachi.com', 'http://www.aboutfaceaz.com', None, 'http://www.pizzanova.com', 'http://www.westowntire.com', '1592168925', 'https://www.potterybarn.com', 'http://www.burritoboyz.ca', 'http://www.oldnavy.com', 'https://firstcu.net', None, None, '1592168939', 'http://www.dontortaco.com', None, 'http://astoriacafemarket.com', 'http://downtownbrewfestival.com', None, 'http://www.papajohns.com', 'https://el-pollito-charro.business.site', None, 'http://www.asiaaz.com', 'https://www.currys.com', 'http://www.discount-drugmart.com', None, None, 'https://www.alamo.com/', 'https://www.coffeeatrio.com', 'https://www.studioemphotography.com/photographer-fairmont-scottsdale-princess', None, None, 'http://www.louiesnoodle.com', None, None, 'http://desertcovenursingcenter.com', 'http://parkviewmanor.ca', None, 'https://www.lumberliquidators.com/ll/stores/az/phoenix/2120-s-7th-street?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1019', None, None, 'http://www.chinapearl1.com/home', 'http://amoving.company', None, 'http://www.macgyverautobody.ca', None, 'https://local.fedex.com/oh/north-olmsted/office-1234/', None, 'http://www.poochesnpalsinc.com', 'http://www.hmsmokeshop.com', 'http://www.bankofamerica.com', 'http://www.a2bmovers.com', 'https://www.casareynapgh.com', None, 'http://www.smilecreationsaz.com', 'https://curaleaf.com/stores/nj', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.rounduplakecampground.com/', 'https://www.sunlifemaids.com', 'https://www.chevronwithtechron.com', 'http://sugarshacksweets.net/', None, 'http://www.stuffingtonbear.com/', None, 'http://www.myflightsurgeon.com', None, 'http://www.stavrossportsbar.com', 'http://www.teffngreens.ca', 'http://www.modern.yoga', 'http://www.fillsgas.com', '1592169057', 'https://local.fedex.com/pa/pittsburgh/office-2064/', 'http://www.scoopnyc.com', 'http://ourjourneytraining.com', None, 'https://www.camelbackautoglass.com', 'http://www.tempespeedandperformance.com', None, 'http://www.spartantrainingchandler.com/', 'http://www.tbirdmed.com', None, None, 'https://www.petsuppliesplus.com/Store/OH/Elyria/Elyria/123?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'http://www.enzositalianmarket.com', 'http://www.drlonlawrenz.com', 'https://www.anylabtestnow.com/franchises/las-vegas-89146/', 'https://stores.jcrew.com/en/south-hills-village', 'http://coachzinger.com', 'http://www.footsensation.ca/', 'http://www.assistbooks.com', None, 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', 'http://www.mcdonalds.com', 'http://www.adore2.com', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://transcanadacarrental.com', 'http://www.berryvinegifts.com', 'http://www.thewellnesscenter.org', 'http://www.lux-spa.com', 'http://www.shopkawaii.com/', '1592169123', 'http://www.playitagainsportsmadison.com', None, 'http://www.audichandler.com/index.htm', None, 'https://www.peets.com', None, None, 'http://www.hollandresidential.com/talise', None, 'http://www.insurrectionaleworks.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.domesticblissdesign.com', 'http://taniahairbraiding.com/', None, 'http://www.graceinlasvegas.com', 'http://www.damcomputermedic.com', 'http://lokacupunctureclinic.com', None, 'http://www.artistsplay.com/hub-cafe', None, None, 'http://www.thrifty.com/?campid=DS:YL_THR_20150109_HP', None, 'https://www.wingstop.com/location/wingstop-421-phoenix-az-85015/menu', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006430792986&ds_s_kwgid=58700000444978510&ds_url_v=2', 'http://cogburnsbar.com', None, 'http://www.kidscoop.org/', 'http://sangrock.com', 'http://www.expertconcretecoatingsinc.com', None, 'http://www.braizenfoodtruck.com/wp1/', 'http://www.drraykim.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.cjsitalianice.com', None, 'http://www.awinadvancedautobody.ca', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Calgary-AB-T2H1L6/840051/', 'http://www.doddslaw.com', 'http://www.stacyspitstopbbq.com', 'http://www.hbotofaz.org', 'http://www.flowershoppetempe.com', 'http://www.moderationsuit.com', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.montzauto.com/', None, '1592169237', 'http://www.foodkingmenu.com', None, 'https://cortland.com/apartments/cortland-whitehall/', None, 'http://tiffanynailshairscottsdale.com/', 'http://www.chocolatsfavoris.com', 'http://www.yogadigs.com/', None, 'http://www.estheticaglenmore.com/index.php', 'http://www.richmondhilltoyota.com/', None, 'http://www.advant-edgecurbing.com', 'http://www.juicestandard.com', None, 'http://nlasvegasvets.com', 'https://footsolutions.com/peoria/', None, 'http://www.themanorspa.ca/', 'http://www.intownsuites.com/locations/charlotte-northeast-chn/', None, None, None, '1592169289', 'http://www.allearzsavannahs.com/', 'http://www.CoronadoHeights.com', 'http://www.aimeecaballero.com', 'http://www.pinklotusmenu.com', 'http://www.myscrubsandmore.com', 'http://www.parmatireservice.net', None, 'http://myvillaroma.com/', 'https://boulderoaksca.com', 'http://www.livingstoninnmadison.com', '1592169315', 'http://www.duffsfamouswings.ca', 'https://www.sourceforsports.ca/en-CA/Stores/3-Adrenalin-Calgary-Source-For-Sports.aspx', None, 'https://budgetbicyclectr.com/used-bicycle-showroom-museum', 'http://arizonagoldendoodles.com', 'http://www.einsteinbros.com', None, 'http://chickenfootestatesales.com', 'http://www.joyli.net', 'http://stuartdayguitars.com', 'http://www.foodlion.com', 'http://www.mellowbentertainment.com', 'http://avenueb-pgh.com', 'http://www.superelectric.tv/pinball', 'http://www.backonthebar.com', 'http://www.dickssportinggoods.com/', None, None, None, 'https://www.6ixcycle.com/contact-us/', '1592169360', 'http://azcountertop.com', 'http://www.turnberrytowers.com', 'http://www.liftedtrucks.com', 'http://elwoodmotorsportsandcollision.com', 'https://www.wellsfargo.com', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1243', None, 'http://www.tntmobiledetail.com', 'http://mariscoensenada.com', 'http://www.rachelsyoungatart.com', None, 'http://www.outback.com/locations/az/gilbert', None, 'http://redmodernfurniture.com', 'http://www.savorcafecharlotte.com', 'https://www.finessecateringandevents.com', 'https://www.petpeoplestores.com/rocky-river-store.html', 'https://www.gregbryandds.com', 'https://www.searsclean.com/pittsburgh-pa', None, 'http://www.cobsbread.com/home/', 'http://www.mcnallyauto.com', None, '1592169413', 'https://palmbeachtan.com/locations/NC/Indian-Trail-Old-Monroe-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=AUG', 'http://www.monroevilleconventioncenter.com', 'http://www.moes.com', None, 'https://www.umcsn.com', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_399', 'http://www.markhambowl.com', 'http://www.maidpro.com/henderson-nv', 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=119&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-119', 'http://www.hairrehabaz.com', 'https://abraauto.com/abra-auto-location/1051-charlotte-nc-albemarle-road', None, 'http://www.gingerflowerstudio.com/', 'http://domenicspub.com/', 'http://www.angelpark.com/-ninos-kitchen', 'http://www.redonionlounge.com', None, 'https://introboutique.com', 'https://www.faema.ca', 'http://johnnyvegasgrill.com/', 'http://www.bakingatitsbest.com', None, 'http://www.phoenixpubliclibrary.org/Locations/Pages/Ocotillo.aspx', None, 'http://www.thedistrictatscottsdale.com', 'https://www.marriott.com/spas/lasjw-jw-marriott-las-vegas-resort-and-spa/spa-aquae/5013971/home-page.mi', None, None, 'http://www.chopstickfoods.com', 'http://www.denimanddiamondsmesaaz.com', 'http://www.azenergy.com/', None, 'http://motorlessmotionbicycles.com', None, 'http://Centurionmgmt.com', 'http://www.crossfitwestvalley.com', '1592169495', 'http://www.oldnavy.com', 'http://www.palaroos.com', '1592169503', 'https://www.libertytax.com/income-tax-preparation-locations/19248.html', 'http://www.timhortons.com', 'http://www.gusbrown.com', None, '1592169513', 'http://www.citypharmacylv.com', 'http://lm2investments.com', 'http://www.silverstatesoccerleague.org', None, None, 'http://www.xlntshutters.com', None, None, 'http://www.tomaydo.com/', None, None, 'https://www.gallusdetox.com', 'http://www.laveenalterations.com', None, 'https://www.redrobin.com', 'http://elcortezhotelcasino.com/', 'http://www.fasttracksolar.com/', 'http://www.maricopaac.com', 'http://www.pagesbooks.ca', 'http://www.shaneonealphotography.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://sites.google.com/publikfire.com/publikfire', None, 'http://www.patatemallette.com/fr', 'http://palmvalleyrehabilitation.com/?utm_source=yelp&utm_medium=organic', 'http://criticalaz.com', 'http://sweetfrogyogurt.com/locations/store/tarentum-pa', 'http://www.kmart.com/stores/nevada/las-vegas/3680.html', 'http://www.snugasabug.com/store', 'http://www.luplv.com', 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-bethany-home?utm_source=yelp&utm_medium=local&utm_campaign=Honorhealth_Medical_Group_Bethany_Home', 'http://www.greatclips.com', 'http://www.toysrus.com/family/index.jsp?camp=MISC:yelp:store:page:tru:111910&categoryId=2255956', '1592169583', None, 'http://www.cherrybombcoffee.ca', None, None, 'http://www.courtneyvista.com', 'http://lisasean.com', 'https://www3.hilton.com/en/hotels/nevada/elara-by-hilton-grand-vacations-center-strip-LASCSGV/index.html?SEO_id=YELP-GV-LASCSGV', 'https://shopused.com', 'http://swingshiftauto.com', 'http://nail-salons.dapeem.com/', None, None, 'http://www.lcbo.com', 'https://www.chick-fil-a.com/lee', 'http://www.starbucks.com/store/9298/', 'http://www.sidestogobbq.com/bbq-location/cleveland-hopkins-international-airport', 'http://www.itsjustlunch.com/', 'http://onestopnutrition.com', None, None, None, 'http://www.jamminjerkvegas.com', 'https://www.lifestorage.com/storage-units/north-carolina/charlotte/28270/109-near-matthews/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NC-109&utm_content=website-link&howheard=IYE', 'https://www.marriott.com/hotels/hotel-information/restaurant/yyzda-delta-hotels-toronto-airport-and-conference-centre', None, 'http://www.dragonpearl.ca', None, 'https://www.gianteagle.com/Stores/Store/?storeId=8%2F', None, None, None, None, 'http://www.adampinksalon.com', 'https://essencevegas.com/locations/las-vegas-strip/', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.blushlasvegas.com', 'http://www.autoglassfactoryaz.com', 'http://www.womensinternational.com', 'https://www.advancedmotionchiropractic.com', None, 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.blastedbarley.com', 'http://www.cvcclub.com', 'http://www.falafelcafecleveland.com', 'http://www.munails.com', 'https://www.gotenda.com', None, 'http://www.coffeerushcafe.com', 'http://www.azdeq.gov/EmissionsTest', 'http://www.RedesignUpholstery.com', None, 'http://www.olbrichbiergarten.com', 'http://doubletree3.hilton.com/en/hotels/ontario/doubletree-by-hilton-hotel-toronto-downtown-YTOCSDT/index.html?SEO_id=YELP-DT-YTOCSDT', 'http://www.northshorecommercialdoor.com', 'http://www.thewhiningpig.com', None, 'http://www.eastmeatswesthalal.com/', None, 'https://www.speedy.com/shops/toronto-danforth/en/', 'http://sandiegonailsphoenix.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.ingleside.com', 'https://soslawnmaintenance.com', None, None, 'http://www.deltamechanical.com', 'https://www.wyndhamhotels.com/hotel/02493?tel=18002521709&iata=00093785&cid=fe:ra:20161215:yl:pp:ramus:02493', '1592169733', 'https://www.speedway.com', 'http://www.gianteagle.com', 'http://www.theredzonemadison.com/', 'https://azcdps.com/locations/paradise-valley/', 'http://www.kitchenland-lv.com', 'http://www.squirrelhilloptometrist.com', 'https://stepuptowellnessnow.com', 'http://www.WestonTeamMortgageLoans.com', 'http://www.dreamlanes.com', '1592169756', None, 'http://www.eatfromatruck.com', None, 'http://www.coffeebytes.net', 'http://tahoepower.net/', None, 'http://www.cafedepariscanada.com', 'http://www.mecklenburgbridal.com', None, 'https://www.lasvegashomes.vegas', 'http://www.DrThompsonAZ.com', None, 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'https://www.ups.com/ca/en/help-center/contact.page', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.capstonerealtypros.com', 'https://ad.doubleclick.net/ddm/clk/459148250;262878939;b', None, None, None, 'https://www.clubpilates.com/tempe/', 'http://www.starbucks.com/', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.tribeamericaleathers.com', 'http://www.bravobridals.com', 'http://www.ipolished.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.vegasonerealty.com', 'https://procellmotorsports.com', None, 'http://www.subzimandi.ca', None, None, None, 'http://www.starbucks.com', 'http://theflatsatgranitereef.com', 'https://www.budsglassjoint.com', 'http://www.city-tavern.com', None, 'http://www.onceuponachildstow.com/', 'http://www.sonoranlifestyle.com/', 'http://auraspacalgary.com/', 'http://tfwestrella.com', 'http://www.lasvegaspaininstitutes.com', 'https://locations.monro.com/oh/fairlawn/111-ghent-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'http://www.doctorsofhair.com/', None, '1592169853', 'https://www.purebarre.com/location/central-phoenix-az', 'http://goodnbr.com', 'http://www.warholdmechanicals.com/', None, 'http://gmhairdesigncolorspecialist.com', 'http://www.michaeljohnsoncpa.com', 'http://robertsidell.com', 'http://www.lakeeriecrushers.com', None, 'https://www.wellsfargo.com', None, 'https://local.fedex.com/nc/charlotte/office-0746/', 'http://www.mrsub.ca', '1592169882', None, None, 'http://www.tempetrophy.com', 'http://www.pvlaserlipo.com/', 'https://www.quicknclean.net', 'https://www.signaturestyle.com/locations/on/toronto/first-choice-haircutters-5677.html', 'http://www.proficientclean.com', 'http://www.einsteinbros.com', 'https://www.kurevapes.com', None, 'https://unlvmedicine.org/family-medicine', 'http://www.7-eleven.com/?yelp=32265', None, 'https://theeggworks.com', 'http://www.aamcophoenixcentral.com', 'http://www.somacafe.com', 'http://www.ronherman.com', 'http://www.culligantotalwater.com', 'http://www.theweaveshop.com/north-carolina-charlotte/', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'http://www.starbucks.ca', 'https://www.bluevaportech.com/', 'http://www.missbrow.com/', 'http://gqcutslasvegas.com', 'http://lasvegas.carenow.com/location/ann-simmons', 'http://allure4me.com', None, None, None, 'http://snvscooters.com', 'http://www.bownessauto.com', None, 'http://cowbridgefurniture.com', 'https://www.staples.com', 'http://www.youngbeautifulsalonspa.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://grilladestorino.com/fr/grillades-torino-place-vertu/', 'https://candy-cravers-coffee.business.site', 'https://www.xpo.com', 'https://www.supercuts.com/locations/oh/lakewood/lakewood-city-center-haircuts-83162.html', 'http://www.carters.com', 'https://arrowheadcoin.com', None, 'http://bytecle.com', 'http://www.bombayschutney.com', 'http://www.bookparkngo.com/index.php?main_page=charlotte', None, 'http://www.familydollar.com', 'http://thedetroiterlakewood.com', 'http://www.crownandanchorlv.com/', 'http://www.papajohns.com/', 'http://www.keffervw.com', 'https://www.choicehotels.com/arizona/scottsdale/comfort-suites-hotels/az816/rates', 'http://www.nardisfinedining.com', 'http://balilaffa.com', 'http://www.cabarruseye.com', 'https://stores.advanceautoparts.com/az/scottsdale/15475-northsight-blvd?utm_content=listing-2017-12-21&utm_medium=local&utm_source=yext&utm_campaign=aap', 'http://www.studiojewelerswi.com', 'http://www.mootowncreamery.com', None, 'https://locations.vitaminshoppe.com/oh/strongsville/vitamins-supplements-strongsville-oh-854.html', 'https://6ixtips.ca', 'http://www.pickeringhonda.com/', 'http://www.ericwelchpainting.com', 'http://www.harborfreight.com', None, 'http://www.childsplayaz.org', 'https://www.beallsplumbing.com', 'http://www.tatesac.com', None, None, 'http://www.roiimprovementsllc.com/', None, None, 'https://nevadaoralandfacialsurgery.com', 'https://www.barrhouseonmain.com', 'http://www.bankandbaronpub.com/', '1592170054', 'http://bluediamondlv.com', None, 'http://www.jfdayspa.com', 'http://www.pizzanova.com', 'https://www.thegalleryapthomes.com', 'http://www.elyriafence.com', 'http://www.bakerykaffeehaus.com', 'http://www.drteddysim.com/about-dr-teddy-sim/', 'http://www.gopropoolservice.com/', 'http://www.redressnyc.com/', 'http://charmeck.org/mecklenburg/county/ParkandRec/Parks/ParksByRegion/NorthRegion/Pages/Jetton.aspx', 'http://www.kbhome.com/new-homes-phoenix', 'http://www.freshbonsainails.ca', None, '1592170086', 'https://www.ediblearrangements.com/stores/2875-W-Ray-Rd-Chandler-AZ-85224', None, None, None, None, 'https://www.prosourcewholesale.com/showrooms/oh-prosource-of-cleveland', 'http://www.merrymaids.com', 'https://www.purchasegreen.com/locations/henderson-nv/', None, 'http://the-toy-box.com', None, None, None, None, 'http://www.buckle.com/', 'http://www.nostalgic-furniture.com', '1592170122', None, 'http://www.maximes.ca', 'http://www.allanimalsrescue.com', 'http://www.streetsvilleflorist.com/?srccode=yelp_track', 'http://www.roadrunnerexpresscarwash.com', 'http://www.cafemia.com', None, None, None, None, 'http://Tshsalon.simdif.com', None, None, 'http://www.rossstores.com', None, 'http://www.dirtyfoodto.com', None, None, 'https://www.bellissimafashions.com', None, 'http://www.dollarama.com/', None, None, 'http://www.azdentalheights.com', 'https://www.discounttire.com/store/az/mesa/s/1294?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://clickserve.dartsearch.net/link/click?lid=43700006430627338&ds_s_kwgid=58700000443429188&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.urbancrawfishstation.com', 'http://www.foothillsrehab.com/', 'http://www.holidayinn.com/hotels/us/en/brampton/ybmca/hoteldetail', 'http://www.eatkickshaw.com/index.php', 'http://www.hannahscaramelapples.com', 'http://center-for-growth.com', 'http://www.lux.salon', None, 'http://robertostacoshop.com', 'http://wagnwash.com/locations/phoenix-az/', 'http://www.thepoolmagician.com', 'http://pierrefonds.carstar.ca', None, 'http://www.riosantafeapts.com/?campaign_code=yelp_Rio_Santa_Fe_AZ_85323', 'http://www.arrowheadmartialarts.com', 'https://www.houseofhandsome.com', None, 'http://kristapsons.com', 'http://www.oldcreditbrewing.com', 'http://www.applehillanimalhospital.com/', 'http://www.ortconline.com', 'http://www.dasgasthaus.ca/', 'http://www.campthunderbird.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.34182.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:34182', None, 'http://www.starbucks.com/store/9298/', None, None, None, 'http://www.cronometro.com', None, 'http://www.salonmichaels.com', 'http://www.burlingtoncoatfactory.com/store-details-Store-213--5959-West-Sahara-Avenue--Las-Vegas--NV--89146-3126.aspx?id=2d282a9a-6b10-4437-bb42-7194af655b83&from=89146', 'http://www.fracosandfroccs.com/', 'http://luchitashudson.com', None, None, 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', '1592170265', 'http://www.hm.com', None, 'http://cranberry.sagahibachi.com', 'http://www.tortoisesupply.com', 'http://www.dominos.com', 'http://www.anchorsuprescuegroup.org', 'http://www.lovemycolon.com', None, 'https://grayhawkgolf.com/dining/the-morning-joint', 'http://etherealnails.com', '1592170292', 'https://www.niudanoodles.com', 'http://www.southwestrainbow.com', None, 'http://ad.doubleclick.net/ddm/clk/283420830;110240480;l', 'http://www.foodtruckcaravan.com', 'http://www.portraitinnovations.com/location/143/OH/Mayfield%20Heights/44124/Mayfield-Town-Center', None, 'http://www.hudsonoverheaddoors.com', 'http://www.meltingpot.com/greenvalley', None, 'http://aguamentiaz.com', None, None, 'http://www.rue21.com', '1592170325', 'http://www.valleyvistapoolcare.com', 'http://www.spirale.net/', 'http://fuegobistro.com/fuegotaco/', 'http://www.liasian.com', 'http://DeconResponseteam.com', None, 'http://www.gurtnerdental.com', 'http://www.timhortons.com/', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'https://www.oakandfort.ca/', 'http://jcls.jazzercise.com/facility/fountain-hills-jazzercise-center-14600', None, 'https://www.marriott.com/hotels/hotel-information/restaurant/cltad-ac-hotel-charlotte-city-center/', 'http://www.dvmcvet.vetsuite.com', None, 'http://plumbingsource.net', 'http://www.middleburgheights.com/?q=rentals_community_center', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', None, 'http://www.sparkletime.net', None, 'http://www.playitagainsports.com', 'http://www.hrcleveland.com/tparrot.php', 'http://www.desertstorage.com/las-vegas-nv-boat-rv-storage', '1592170380', 'http://www.nakedcitylv.com', None, 'http://www.bathandbodyworks.com', None, 'http://www.hoipolloicafe.com', None, 'https://druxys.com/location/2-st-clair-ave-colonia-place/', 'http://www.plazahotelcasino.com', None, None, 'http://www.thespiritbox.com', 'https://www.patagoniaelements.ca/store/content/10/Calgary/', '1592170409', None, None, 'http://www.countrytireautomotive.ca', 'https://www.royaldistributing.com', 'https://www.presidentialpools.com/gilbert-swimming-pool-builder', 'http://www.gingersdesserts.com', None, None, None, 'http://www.vegasairductcleaning.com', None, 'http://www.betterlifemobility.com', 'http://www.azoral.com/', 'https://www.bellacinosofstow.com', '1592170442', 'https://totalimageoakville.biz', 'http://www.dayonepizzadelivery.com/', None, None, 'http://desotocentralmarket.com', None, 'http://www.eyedoctorchandleraz.com', None, 'http://eosfitness.com/location/pecos?utm_campaign=vegas-pecos&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', None, '1592170464', None, None, 'https://stores.jcpenney.com/pa/pittsburgh/clothing-stores-pittsburgh-pa-2263.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2263', None, None, 'http://www.thepamperedpinkie.com/', '1592170483', None, None, 'http://www.flightcentre.ca/', 'http://www.marshallsonline.com', '1592170491', 'https://www.gilbertaz.gov/departments/parks-and-recreation/parks-facility-rentals/parks-info-ramada-rentals/parks/crossroads-park', 'http://www.pair.com', '1592170499', 'https://organicnaillounge.business.site', None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.mathnasium.com/northwestlasvegas', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.eddietaxplus.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=3317&localechange=1', 'http://www.heroburgers.com', 'https://www1.shoppersdrugmart.ca', 'http://www.sackstierney.com', 'http://www.beastmodeonline.com', 'https://www.waxmans-carpet.com', 'http://myazinjury.com', 'http://www.mrappliance.com/east-valley', None, 'https://www.aritzia.com/en/store?StoreID=aritzia-bloor-flagship-toronto', 'http://www.northcalgarypediatricdentistry.com', 'https://skylineliquorstores.com', None, None, 'https://womensfitnessclubs.com/ajax/?utm_source=yelp&utm_medium=search&utm_campaign=yelpcampaign', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.siennalv.com', 'http://www.tomohibachiandsushi.com/', 'http://www.marriott.com/phxrn', None, None, 'http://www.avis.ca/', None, 'http://www.barriquesmarket.com', 'http://www.spirithalloween.com/', None, 'http://www.bigbenbarber.com', 'http://www.andoaz.com', 'http://www.klassykidsacademylv.com/', 'http://www.freddysusa.com', 'http://repweddings.com', None, None, 'https://www.voguerecoverycenter.com', '1592170593', None, None, 'https://www.planetfitness.com/gyms/streetsboro-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=13080', None, 'https://hawkesclinic.com', None, 'https://www.johnnyscleveland.com', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Sun%20Prairie/WI/3289', 'http://libertyshawarma.com', None, 'http://www.altatempe.com', None, 'https://angel-dentalcare.com', 'http://www.pvcglendale.com', 'http://www.letspartyconsultants.com', 'https://www.wyndhamhotels.com/hotel/53380?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:53380', None, 'http://www.v-dubfurniture.com', 'http://www.sovpreschool.org', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.physio-logic.com', None, 'http://www.buca.ca/king.html', 'https://www.100thbgrestaurant.com', 'http://www.arizonaeyes.net', '1592170657', None, 'http://www.dollarama.com/', None, 'http://www.foxspizzamtwashington.com', None, 'https://stores.jcpenney.com/nv/lasvegas/clothing-stores-lasvegas-nv-2848.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2848', None, None, None, 'http://www.GoodByeDebt.com', 'http://www.starbucks.ca', 'http://www.icecastlearena.com', 'http://www.bestmatt.com/', None, 'http://www.fix8fitnesscafe.com', None, 'http://proem.org', None, None, None, 'http://www.sojoblau.com/', None, 'http://www.canyonstateedu.com', 'http://www.weavebaratl.com', 'http://www.assemblychefshall.com', None, 'https://dealer.sprint.com/preferred-wireless/find-a-store/67331-bridgeville-pa-15017', None, 'https://www.hydroplumbinginc.com', 'http://www.johnwallickjewelers.com', 'http://www.roastednutfactory.ca', 'http://www.hottopic.com/', 'http://www.azulorganicskincare.com', None, None, 'http://www.joyestes.net', 'http://www.jambajuice.com', None, 'http://www.traditionalelectric.ca', 'http://www.hatchyoga.com', None, 'http://www.harbsauto.com', 'http://www.TheKyotoBowl.com', 'http://www.sunnyviewdental.ca/georgetown', 'http://www.inkbombaz.com', 'http://locations.traderjoes.com/oh/woodmere/676/', 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', None, None, 'http://www.bulkbarn.ca/', None, None, 'https://www.supercuts.com/locations/az/surprise/albertsons-shopping-center-haircuts-82334.html', None, 'http://www.applewoodstorage.com', None, '1592170796', None, 'https://theprimerestaurantphx.wordpress.com', None, 'http://fitlifefusion.com', 'http://pazzoscatering.com', 'http://kaffirlimeindonesiancuisine.blogspot.ca', 'http://www.comicoasis.com', None, 'http://www.bigbztexasbbq.com', 'http://www.mrservice.ca', 'http://perennial-yoga.com', 'http://www.lovenspoonfuls.net', 'https://www.davidwmartinlaw.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.kireitoronto.com/', 'https://www.directcarpetone.com', 'http://www.bestratereferrals.com', None, '1592170850', 'http://www.dimpflmeierbakery.com', None, 'http://fabulashclt.com/', 'https://www.georgesflowers.net/?srccode=yelp_track', None, 'https://mintdentallasvegas.com', 'http://www.summerlink.com/wp-content/uploads/2010/03/2010ParkMap', None, 'http://www.southpittsburghvet.com', None, 'http://www.hpsc.ca', 'http://atlanticdentalphoenix.com/', 'http://www.middletonsports.com', 'http://www.californiathai.ca', 'http://www.albertaparks.ca/fish-creek.aspx', None, 'http://summitrestorationlv.com', 'http://serviceprowashandlube.com', 'http://bobcoffeebar.com', 'https://www.lhmfordmesa.com', 'http://www.dailyfreshgrillandcafe.com', 'http://www.houseofblues.com/lasvegas/crossroads', 'http://www.owensautorepair.com', None, None, None, 'http://www.halisangels.com', '1592170925', 'http://www.elixirspa.ca', 'http://www.phillyssportsgrill.com/', 'http://www.charlottecomedytheater.com/', 'http://www.dutildenim.com', 'http://www.treasureisland.com/restaurants/khotan.aspx', 'http://painstopclinics.com/pain-clinic-uptown/', None, 'https://www.modlash.net', None, None, 'http://www.cledogwalk.com', 'http://drivetime.com', '1592170963', 'http://www.bankofamerica.com', None, 'http://www.skyloft.com', 'http://nodayoga.com/', '1592170978', 'http://www.boosterjuice.com', 'http://www.letusrollyouone.com', None, 'https://www.anytimefitness.com/gyms/1069/Pineville-LA-71360/', 'https://iflycu.com', 'http://www.ysl.com/gb', 'http://www.southsidemotorspgh.com', 'https://www.ribeirojiujitsu.com/las-vegas-nevada.html', 'https://www.wellsfargo.com', None, 'https://medmen.com/stores/tempe-airport-phoenix-sky-harbor', None, None, 'http://www.allisonlovesfinejewelry.com', None, 'https://www.uhaul.com/Locations/Truck-rentals-near-Champaign-IL-61820/760043/', 'http://www.ojoslocos.com', 'http://beitshofarot.com', 'http://www.key.com', 'http://www.rainbowchiropracticcenter.com', 'http://www.rivenailandskincarespa.com', 'https://www.pancheros.com/locations/fitchburg', 'https://www.smilesquadlv.com', 'http://www.southfacese.com', 'https://www.bankofamerica.com', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', None, '1592171054', None, 'http://Rentmyrims.com', '1592172433', 'http://www.nevadaspca.org', None, 'http://extremecleantoday.ca/', None, 'http://www.runningroom.com', 'http://www.primarypetcare.com', 'http://www.extremeautocustoms.com', 'http://www.drivingforce.ca', 'http://www.clarkbrands.com', 'http://www.ilovemichaels.com/', 'https://hansenfamilyplumbing.com', 'https://www.ductz.com/north-phoenix-deer-valley/', 'http://www.klosekniturbana.com/', 'http://purebarre.com', None, 'http://renewedbeautyspecialists.com/', 'https://elevationchurch.org/locations/blakeney/', 'http://www.goodlifefitness.com/', 'https://www.selfstoragesolutions.com/self-storage/az/gilbert/85297/421?utm_source=yelp&utm_medium=cpc&utm_campaign=Gilbert', None, None, None, None, 'http://www.drainproplumbing.com', 'http://www.Charleys.com', 'http://www.mtsystems.ca/', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.olivegarden.com/locations/az/scottsdale/scottsdale-e-cactus-rd/1234?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:scottsdale-az-1234_pl:locurl_rd:1175', None, 'http://www.woofswigglesnwags.com', None, None, None, 'http://www.lasvegasnannies.com', 'http://www.sixthcitycycles.com', 'https://fancypetsaz.com', 'http://haymakersportsgrill.com', 'http://Elegantentrysarizona.com', 'http://www.avalonmeatcandy.com', None, 'http://www.theargusrealestatecompany.com', '1592172552', 'http://www.pizzasola.com/eastside.html', 'http://www.arizonabartenders.com', None, None, None, 'http://www.morningstarstorage.com/location/308/sc/fort-mill/carowinds/?ref=yelp', 'http://www.dynamitemontessori.com/', None, 'http://aandbroofing.net', 'https://www.kenganleynissan.com', 'http://www.janthonysalonspa.com/', 'http://rawlicious.ca/canada/locations/markham', '1592172590', 'http://www.illinistor-it.com', None, 'http://www.truevalue.com/mcfarlandtruevalue', None, None, None, None, 'https://www.brakesplus.com', 'https://www.scottsdaleaz.gov/parks/scottsdale-civic-center', 'http://www.athenaswindows.com', 'http://fishkinggrill.com', 'https://locations.davidstea.com/ab-calgary-111', 'http://www.salaradesserts.com', None, None, 'http://www.belle-image.ca/', None, None, 'http://bootlegsmokehouse.com', 'https://www.jasonsdeli.com/restaurants/maryland-pkwy-deli', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', '1592172650', 'http://gotorickys.com', 'http://www.morrowparkcityapts.com', 'http://epicentrenc.com', 'http://www.marketonmacleod.com', '1592172664', None, 'http://subsecreto.com', 'http://www.Barking-Dogs.com', 'http://www.punjabitadka.ca/', None, None, 'http://southeastcrabfeast.com/', 'https://www.tanrepublic.com/locations/nevada/las-vegas/maryland-parkway', 'http://www.mattressfirm.com/', 'http://www.greathousesportsgrill.com', 'http://www.thaihouse.us/', 'https://www.aircanada.com/us/en/aco/home.html', 'http://www.substationii.com', 'http://www.greatwallchinese-lasvegas.com', 'https://www.childhelp.org/advocacy-centers/childrens-center-of-arizona/', None, 'http://www.therefinerycc.com', 'http://onsitetinter.com', 'http://harvestcompassioncenter.org', None, None, None, 'http://www.ohstudiolv.com', 'https://sgplaw.com', 'http://www.failteirishpub.ca/', None, 'https://stores.loft.com/outlet/us/nv/las-vegas/7400-las-vegas-blvd-south.html', 'http://www.paradisebakery.com/', 'http://www.osigym.com', None, None, 'https://www.uniquenailbargateway101.com', 'https://www.quarryparkchiropractic.com', 'http://www.easternfootspa.ca', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://paintingwithatwist.com/avon/', 'http://www.urepmaids.com', 'http://www.entebella.com', None, None, 'https://www.springboardrecovery.com', None, 'http://www.pekingexpress.ca', None, None, 'http://www.red9ine.com', 'http://swift-moving.com', 'http://www.frontgate.com/Frontgate/US/CustomerService/Scottsdale/landing-path', 'http://www.greatexpressions.com/dental-offices/ohio-offices/severance', None, None, 'https://www.ulta.com/stores/macedonia-oh-1004', None, None, 'https://www.sitesmartmarketing.com', '1592172812', 'https://www.hilton.com/en/hotels/phxsrhx-hampton-suites-phoenix-surprise/?SEO_id=YELP-HP-PHXSRHX', 'http://patriciangrill.com/', 'http://www.1800waterdamage.com/phoenix-az', None, None, 'http://www.theelranchomotel.com', 'http://falbobrospizza.com', None, 'http://www.noahsnaturalfoods.ca', 'http://vitalshipmed.com', 'https://www.walgreens.com/locator/walgreens-4900+library+rd-bethel+park-pa-15102/id=11296', None, 'http://www.aboutadog.ca/', None, 'http://www.palacestation.com/entertainment/jacks/?utm_term=PS&utm_content=PS-PROPERTIES&utm_medium=SOCIAL&utm_source=YELP&utm_campaign=PS-YELP', None, 'http://www.telaverdeapts.net', 'http://www.skinpossible.ca', None, 'https://www.fordonfifth.com', None, None, 'http://www.gamestop.com', None, 'http://www.rentawrecktoronto.com', 'http://www.fitworks.com/rockyriver', 'http://www.calderawealth.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://extendedstayhotels.com', 'http://jc101services.com', 'http://www.palladinoscleaning.com/', 'https://www.haydenparkapartmenthomes.com', 'http://www.cyclepathnorthyork.com/', 'http://www.starbucks.com/store/69863/', None, None, 'https://www.visioncenterslv.com', None, 'http://makeupmagic.net', None, 'http://therapeuticmethod.net', '1592172922', 'http://www.tlc-airconditioning.com', None, 'https://urbanlivestockvet.com', None, 'https://www.nvisioncenters.com/locations/las-vegas/nevada-eye-care-east/?utm_source=directory&utm_medium=yelp', 'https://www.spectrumdermatology.com', 'https://www.intownsuites.com/extended-stay-locations/arizona/phoenix/west-2/', 'https://beautyenhancementsbyd.com', 'http://www.veneziabakery.ca', None, None, 'http://www.dentscharlotte.com', None, 'http://www.pethavenaz.com', None, 'http://exclusivelytankless.com', None, None, 'http://insurance-agency.amfam.com/AZ/tryna-hoerger-owens/default.aspx?sourceid=agp0001015578', 'http://laterna.ca/', None, 'http://affordableframingaz.com', None, 'http://blackcablimo.wix.com/blackcab', '1592172980', 'http://www.newfoodorder.com', 'http://lolasgelato.ca', 'http://www.tonibulloni.com/', None, None, None, 'http://www.rebath.com/location/lasvegas', 'http://www.acuhealings.com/', 'http://viapanini.ca', None, 'https://www.wyndhamhotels.com/hotel/14408?tel=18008899735&iata=00065402&cid=fe:hj:20170523:yl:pp:hjus:14408', None, None, 'http://ccsunscreens.com/', 'http://tazikiscafe.com/location/charlotte', '1592173013', 'http://www.effortlessmobileauto.com/servicesPhoenix/servicesPhoenix.html', 'http://fukuburger.squarespace.com', None, 'http://www.empowerpt.com', None, 'http://khalsamontessori.org/', 'http://www.mayfieldnissan.com/', 'http://quintealias.com', 'http://www.starbucks.com/store/9229/', None, 'http://www.fatburger.com/home/', 'http://cvdentalcare.com/contact-us-citrus-valley/', 'http://www.bonniesyarncrafts.com', 'http://www.nedrebos.com', 'http://www.ThePMFirm.com', None, 'https://www.xmsweetconnections.com', None, '1592173062', None, 'http://www.ivandianaphotography.com', 'http://www.dunkindonuts.com', '1592173071', 'http://www.cbac.com/sun-prairie?utm_source=Social&utm_medium=Yelp', 'http://www.threebrothersbarandgrill.com', None, 'http://www.cabinforlife.ca', None, 'https://www.azsolarconcepts.com', 'http://mwsvegas.com', 'http://scottsdalecosmeticdr.com', 'http://www.southsidejewelers.com', None, 'https://www.drtroell.com', 'https://www.coolrunningsautomotiverepair.com', 'http://www.stop-n-go.com', 'https://www.zimbrickchevrolet.com', 'http://www.preciouspets702.net', 'http://www.structube.com', 'http://www.middleroadbarbershop.com', 'https://karenshallmarkshops.com', 'http://www.midaslocator.com/AutoRepairFinder/tabid/151/Default.aspx', 'http://www.springdayspa.com', None, 'http://ridgeparkurgentcare.com', 'https://www.spectrumeyecarenc.com', 'http://vinoandpanino.com', 'http://orangeleafyogurt.com', 'http://weddingsbybonnie.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.richardmilleusa.com', 'http://www.chaneyscollision.com', 'http://www.townshoes.com/', 'http://www.indulgeyourselfsalon.com/', None, 'https://www.luxurypad.vegas', 'http://wanleeloy.com/', 'http://mindbrainlv.com', 'https://www.eatnpark.com', 'http://lerock403.com/', 'http://www.quiznos.com', 'http://www.crossfitculmination.com', None, None, 'http://www.shadowridgeapartmenthomes.com', None, 'http://le-cue.com/', 'http://www.carolinashealthcare.org', 'http://americanbrosplumbingco.com', 'http://www.thepalmsapts.com', None, 'http://www.bk.com', 'http://www.daracap.com', 'http://www.selectphysicaltherapy.com', 'https://www.premierworkspaces.com/nevada/henderson-augusta-park?utm_campaign=Yelp&utm_source=Yelp%20Organic', 'http://www.aulaz.com', 'https://locations.whataburger.com/az/goodyear/14251-west-indian-school-bypass.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', 'http://bullandfinchbars.com', 'http://www.harkinstheatres.com/theatreDetails.aspx?theatreId=4527', None, 'http://www.stfrancisdesaleslv.org', 'http://www.SallyBeauty.com', None, None, 'http://www.ljsilvers.com', None, '1592173210', 'www.brokenplate.ca', None, 'https://www.taylorstmgmt.com', None, 'http://www.swrandalltoys.com', 'http://www.factorydirect.ca', 'https://champsfamilyautomotive.com', 'http://www.orbitzcleaning.com', None, 'https://www.choicehotels.com/pennsylvania/pittsburgh/sleep-inn-hotels/pa744/rates', 'http://www.krispykreme.com', None, 'http://www.jacksonpt.com', None, None, None, None, 'http://www.6az.com/', 'http://www.ynhcclinic.com/', 'http://www.altafillmore.com', None, 'http://www.untitledandco.com', 'http://www.thesodashop.co', 'https://www.themarketphx.com', 'http://www.dqlunchforless.com', 'http://www.yourmovingsolutions.com/?utm_source=Yelp', 'http://miketheplumbercharlotte.com', 'http://www.lasvegasjeepandoffroad.com', 'http://www.oldnavy.com/products/las-vegas-nv-store-5811.jsp', 'http://www.starliquor.ca/', 'http://www.thefrenchbee.com', 'http://www.jeffsnotary.com/', None, None, 'http://pettis-pizza.com', None, 'http://www.rajdhanisweets.ca', 'http://www.simsgm.com/', None, 'https://joefilter.com', 'https://www.maaco.com/locations/az/glendale-11376/', 'http://www.pandaexpress.com/', 'http://www.meineke.com/', 'http://www.dunkindonuts.com', 'http://www.urbanhakka.ca', None, 'http://www.sweetrubyjane.com', None, None, None, 'http://www.legacybungalowsapts.com', 'http://www.getbooked.com', 'https://www.moes.com/find-a-moes/pennsylvania/murrysville/3428?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://www.mrpuffs.com/', 'http://www.dibeads.com', 'https://www.carstar.ca/en/locations/ab/calgary/carstar-calgary-sunridge-16118/', None, 'http://www.colormebella.com', 'https://www.wilhelmautomotivelitchfield.com', 'http://www.valleverdecarwash.com', None, 'http://www.lapetite.com/your-local-school/las-vegas-nv-7300/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'https://local.fedex.com/nc/gastonia/MRNA/?cmp=LOC-1001545-3-2-971-1110000-US-US-EN-YEXTLISTFEDEXSC', None, 'http://www.escapeloungelasvegas.com', 'http://azlifts4less.com', 'https://scottsdaleair.com', None, None, 'http://www.studiofivehair.com', None, 'http://www.insidethebungalow.com', 'http://www.health4lifenv.com', 'http://www.llbcpa.com/#dxEvq', 'http://www.fantasticsams.com', 'http://www.greatclips.com/', None, 'http://www.carolinafireplacerepair.com', None, 'http://www.dickies.com', None, 'http://www.cavabienspa.com/', None, None, None, 'http://beijingchinesecuisine.com', 'https://www.shoeshow.com', 'http://www.orangeleafyogurt.com', 'http://www.starbucks.com/store/8054/', None, None, None, 'http://www.sunshinemoon.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.stevesultimateair.com', 'https://www.wingstop.com/location/wingstop-1117-cleveland-oh-44128/menu', None, 'http://www.inspectslasvegas.com', None, None, None, 'http://www.barefoot-acupuncture.com/', 'http://www.kxyorkville.com/', 'http://flamebroilerusa.com', None, None, None, 'http://www.dragongemchinese.com/', 'https://www.collegecutiescleaningcars.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.fieldservicesaudio.com', 'http://www.lasvegastransportation.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.redrockcanyonlv.org', 'http://www.yongesheppardcentre.com', None, None, 'http://locations.jjill.com/az/scottsdale/65', 'http://www.savourfinefoods.com', 'http://www.twosphotobooth.com', 'https://ccv.church/locations/midtown-phoenix', '1592173504', None, None, None, 'http://www.pmcpropertygroup.com/', 'http://www.citywidemovers.ca/', 'http://www.apnursery.com', 'https://www.extraspace.com/storage/facilities/us/california/glendale/299955/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, 'http://www.sndk9.com/', 'https://local.pharmacy.safeway.com/az/scottsdale/7920-e-chaparral-rd.html', 'https://zoeskitchen.com/locations/store/az/mcdowell', '1592173529', None, 'http://kickinkitchenfoodtruck.com', None, 'http://www.lxvestudios.com', 'http://www.themugshottavern.com/', 'http://www.kravelasvegas.com/', None, 'http://www.noodlewok.com/', 'http://www.gigiscupcakesusa.com/ahwatukee-arizona', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.classictattoowilloughbyoh.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'http://www.davidduncanhouse.com', 'http://www.Totallymadeover.com', None, 'http://www.cccakesbybrandi.com', 'http://www.thankqrentals.net', '1592173562', None, None, None, None, 'http://www.grcogrill.com', 'http://www.cantinalaredo.com/location/scottsdale-arizona/', 'http://www.japaneats.ca', None, 'https://www.esso.ca/en/gas-station/vaughan-on-majormacvelloreesso-200302606', 'http://www.jordansrefurbishing.com', 'http://www.gyrostown.com', 'http://www.eddiebauer.com', None, 'http://www.serenityspalounge.com', 'http://www.timhortons.com', 'http://www.iphotoshop.com/', 'http://h5helicopters.com', 'https://www.fahadrestaurant.com', 'http://www.relocationservicescanada.ca', 'http://redcanyondentistry.com', 'http://www.quaker.org/pghpamm/', 'http://www.loveyourposture.com', 'http://www.manilabbq.com', 'http://www.kelseys.ca', None, 'http://www.baskinrobbins.com', 'https://www.boutiquewebsites.ca/website-designs.html', None, 'http://www.decatarina.com', 'http://www.felixswimschools.com/locations-schedules/woodbridge', 'http://www.magictouchmobiledetail.com', 'http://www.shenandoahmill.com', 'http://www.lovinghut.ca', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FLASHH', 'http://www.molonlabe.com', None, None, 'http://www.bundlebuilders.net', 'http://www.thebrewteabar.com', '1592173643', 'http://thecellarsalon.com', None, 'http://carambamex.com', 'http://villagepubcasino.com', None, 'http://www.cainpark.com', 'http://www.fairwaysapartmenthomes.com', 'https://www.athome.com/store-detail/?StoreID=North%20Carolina-Charlotte&utm_source=yelp&utm_medium=paidprofile', 'http://www.midas.com/toronto/store.aspx?shopnum=9827&dmanum=857001', None, 'https://www.bannerhealth.com/locations/phoenix/surgicenter', 'http://www.bestdealsauto.ca', 'http://www.dunkindonuts.com', None, 'http://dekra.us/en/nevada/henderson-26-w-horizon-ridge-pky/', 'http://www.pizzapizza.ca/', 'http://www.urbanfarm.org', 'http://fairgreenlawncare.com', 'http://www.flamingicecube.com', 'http://tnailslasvegas.com/', 'http://countrybarpeoria.com/', 'http://www.magicofjasonbird.com', 'http://kidsinclearningcenters.com/chandler-watermark/', 'http://www.jimenezarmsinc.com', 'https://www.squawpeakhilton.com/dining?_ga=2.50950569.1853949617.1562623293-1431667612.1561583712', 'http://www.madisontranquilitymassage.com', None, 'http://spgilbert.com', 'http://www.siamthaipgh.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.doraziolawgroup.com', 'http://www.highlandinnlasvegas.com', 'https://www.uhaul.com/Locations/Trailer-Hitches-near-Charlotte-NC-28217/780053/', 'https://www.walgreens.com/locator/walgreens-6906+university+blvd-moon+township-pa-15108/id=10917', 'http://www.rinxtoronto.com', 'http://kingskitchen.org/', 'http://www.wholehealth4life.org', None, 'http://www.velocityautobody.com', 'http://www.hotpinkteahouse.com', None, 'http://www.showtimetourslv.com/', 'https://www.dominos.com', None, '1592173746', 'https://us.petvalu.com/location/6058', 'http://illinois.edu', None, 'http://www.arizonaeliteproperties.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', '1592173758', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.missspice.ca', 'http://www.24-7electricalservices.com/', None, 'http://www.familydollar.com', 'http://bchcares.org', 'https://www.walgreens.com/locator/walgreens-2324+w+war+memorial+dr-peoria-il-61614/id=6408', None, 'http://www.unforgettablecoatings.com/', 'https://www.purebarre.com/location/fort-mill-sc', 'http://www.starbucks.com/store/9289/', '1592173785', 'http://someburros.com/', 'https://chatters.ca', 'http://salsaritas.com', 'http://www.barbiesgrill.com', None, 'http://www.cleyards.com', 'http://www.onenevada.org', 'http://www.spectrac.com', 'http://www.hortfrontiers.com', None, 'http://pursuitcf.com', None, None, 'http://www.qcreflex.com/', 'http://www.azwhiteningspa.com/index.html', 'http://www.houseofathens.com', 'http://www.firstclassprinting.ca/', None, 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://crissangel.com', 'http://TignorGroup.com', 'http://www.davismagic.com/', 'https://www.kellerhearing.com', 'http://www.cannabisclinics.ca/medical-marijuana-canada-clinic/#1440516223690-62dfe946-9e59', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=976', 'http://www.oasisbeautyspa.ca', 'http://www.sushiplus.ca/', '1592173848', '1592173850', 'http://www.searshometownstores.com/home/az/fountain-hills/1841', '1592173854', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', None, None, None, 'http://www.furnitureworld1.com', None, None, 'http://www.bellagioapts.com/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', None, None, None, 'https://cell-computers-and-games.business.site', '1592173881', 'https://mamajuliannes.com', 'https://backyourhero.com', 'http://www.theplacerestaurant.ca', 'http://www.urbanbulkandrefill.com', 'https://www.lumberliquidators.com/ll/stores/nc/matthews/11101-east-independence-blvd?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1264', None, 'http://www.marengospa.com', 'http://dialabottle.ca', None, 'https://ad.doubleclick.net/ddm/clk/434342189;236814625;k', None, None, 'http://riotanlasvegas.com/wordpress1/', None, 'http://www.alyciamoore.com', 'http://abdappraise.com', 'http://www.fatbastardburrito.ca', 'http://abakeshop.com', 'http://www.mesabilliards.com', None, 'http://www.marbleslab.ca', 'https://townandcountrybarbershop.com', None, 'http://www.covenantday.org', 'http://www.lakenormanpaintandbody.com', None, None, 'http://www.elitemassagecalgary.ca', 'http://www.cccnevada.com/doctor/g-h-kashef-md/', None, 'https://www.huntington.com/Community/branch-info?locationId=23476', None, 'http://www.bivfaz.com', 'http://www.metro.ca', 'http://www.vegashot.com', 'http://www.crossroadsvet-painesville.com', 'http://www.baskinrobbins.com', None, 'http://www.XtremeExtensions.com', 'http://www.arbys.com', 'http://www.scottsdaleaz.gov/preserve.asp', None, '1592173969', None, 'http://vivaviolins.com/', 'http://www.fionnmaccools.com/locations/brampton-ray-lawson', 'https://www.wingstop.com/location/wingstop-421-phoenix-az-85015/menu', '1592173979', 'https://www.sprouts.com/stores/details/-/store-details/view/store/2/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://www.maidpro.com/phoenix-north', 'http://www.kingputtlv.com', 'http://mysuboxonedoctor.com', 'http://www.ivylasersalon.com', 'http://www.kofeinstitute.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.laredosrestaurante.com', 'http://www.wizardofsuds.net', 'http://www.ontarioparks.com/park/voyageur', None, 'https://excelprimarycare.com', None, None, 'https://www.malakjewelers.com', 'http://www.clevelandishome.com', 'http://www.pattysheart.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.marrakechrestaurant.ca', 'http://the-yellow-penthouse.business.site', None, None, None, 'http://www.jjbrewco.com', 'http://www.piccoloantiquemall.com', 'http://www.divinethreading.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.allthingstea.ca', 'http://www-rivera-custom-painting.com/PROFILE', 'http://www.moxieinkdesigns.com', 'http://www.royaljade.ca', 'https://honorhealth.com/locations/primary-care/honorhealth-medical-group-east-tempe', 'https://www.napaonline.com', None, None, 'http://www.abpreschool.com/', 'http://www.ryanssalons.com', 'http://www.scottsdaleaz.gov/parks/cactuspool.asp', 'https://carolinacleanerscharlotte.com', 'http://www.goldsgymcalgary.ca', None, 'https://diceandbeansboardgamecafe.com', None, None, 'https://www.desertfinancial.com/Home/BranchDetails?branchId=1', 'http://www.trendautomotive.com', None, None, 'http://www.isaacjewelers.com', None, '1592174106', 'http://www.ashfordplaceapartments.com', 'https://store.vioc.com/nv/las-vegas/9631-trailwood-dr-89134-HC0003', '1592174114', '1592174118', None, None, None, 'http://pitapitusa.com', None, 'http://meridianlv.com/', None, 'https://www.casinoarizona.com/dining/eagles-buffet/', None, None, None, 'http://www.haggen.com', 'http://www.brickpointingpittsburgh.com', None, None, None, 'http://pennhills.org', 'http://rrrc.run', 'http://www.sunterramarket.com', 'http://www.pastorsautoservice.com', 'http://lvhottubs.com', 'http://l.macys.com/university-heights-oh?cm_mmc=Yelp_Stores-_-UniversityHeights-_-n-_-578&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=University+Heights_578&m_ac=yelp_stores&m_ag=n', None, 'http://www.mychickenshack.com', 'http://angelschristianacademy.com/landing.php', None, 'http://www.housing.wisc.edu/universityapartments/eheights', 'http://www.evaszabo.com', 'http://www.dentalemergencyservices.ca', None, None, None, '1592174202', 'https://container36.wixsite.com/wtrn', 'http://www.artisanhairstudio.net', 'http://www.desertheatwindowwash.com', 'http://www.thedoctorfence.com', None, None, '1592174224', None, 'https://www.choicehotels.com/north-carolina/charlotte/suburban-hotels/nc533/rates', 'http://www.goodmanslandscape.com/', None, None, None, '1592174241', 'http://www.getthelook.com/salondetail/default.asp?salonid=61146', 'http://www.adamsroadsidetowing.com/', None, None, None, 'http://www.aalltechmobile.com', 'http://www.hoopdome.com', None, 'http://www.nrsinjurylaw.com', None, 'http://www.coldwaterroofing.com', 'http://www.MassagesByChelsa.squarespace.com', 'https://www.wallacebethelparkflower.com', None, 'https://www.richerlifecounseling.com', 'https://someburros.com', None, 'http://marcelos-az-barbershop.business.site', None, None, 'http://cowtownbeefshack.ca', 'http://cooperscarpetandtilecleaningaz.com', 'http://alexbeauregard.com', None, None, '1592174306', None, None, None, 'http://www.wrapcitydesigns.com', None, 'http://www.southshoresah.com', 'http://www.balzacs.com/locations/distillery-district/', '1592174326', 'https://npidb.org/organizations/physician_assistants/family_363lf0000x/1386110443.aspx', None, None, None, None, None, None, 'https://www.americandiscountfoodsaz.com', 'http://www.JenniferKostuchowski.MyHomeHQ.biz', 'http://www.sweetdaddycupcakes.com/locations.html', None, None, 'http://www.drbarin.com', 'https://nuancelasvegas.com', '1592174369', None, 'https://www.petsmart.ca/stores/ca/on/scarborough-store2009.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', 'https://goppa.org', None, None, 'https://www.perplexitygames.com', 'http://www.printystamp.com', 'https://alfredopatisserie.com', 'http://ipacupuncture.com/', None, 'https://hirosushi.to', 'http://www.verizonwireless.com/', 'https://www.peopleready.com/locations/las-vegas-nv-1144', 'http://hancockfabrics.com/', None, 'http://www.welltracnv.com', 'http://www.greenstarautocenter.com', 'http://www.pmkbar.com', None, None, None, None, 'http://www.bhhsnv.com', 'http://www.dhslv.com', None, 'http://www.airportparkingreservations.com/lot_ez_airport_parking_yyz', None, 'http://www.andysfishandchips.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1212+South+Greenfield+Road-Mesa-AZ-85204/storeid=5026?cid=ps_ylp_2020', None, None, 'http://www.alwaysjumping.com', 'https://www.mimiscafe.com/locations/glendale/', 'https://www.streetsideclassics.com', 'https://healinghandshannah.com', 'http://www.wendys.com', 'https://nationwidevision.com/locations', 'http://www.canadiantire.ca/en/store-details/on/toronto-main-danforth-on.store.html', None, 'https://globalautoscarrentals.com', 'https://www.sonoraquest.com/find-a-location/phoenix-by-appointment-only-tatum-shea/', 'http://www.gnc.com/', 'https://www.residentculturebrewing.com', 'http://www.ucalgaryrecreation.ca', 'http://www.sheaparc.com', None, 'http://www.windowuniversecleveland.com', 'http://www.marvelousmousetravels.com', None, '1592174529', 'http://www.eraagelessfuture.com', 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', None, 'http://www.gap.com', '1592174544', 'http://www.floweramacleveland.com', 'http://www.mycdi.com/arizona/insight_imaging_-_arrowhead/', None, None, 'http://www.perfectblend.ca', 'https://locations.theupsstore.com/pa/moon-township/5990-university-blvd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.laseraway.com/locations/nv/las-vegas/?utm_source=yelp+organic&utm_medium=website+link', 'http://www.fabfred.com/locations/trailwood-drive/', None, 'http://www.srsengineshop.com', 'http://studiooftens.com', '1592174581', None, 'http://www.pcfarm.ca', None, 'https://www.cartelcoffeelab.com/pages/5th-avenue', 'http://www.disantopizza.com', None, 'http://www.heritagefishnchips.com', 'http://www.needle-pin.com', 'https://speeders.ca/calgary/', 'http://www.countryhillsmassage.com', 'http://www.fedmc.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360246&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://tempeautoshop.com', None, 'http://www.silverstatecu.com', 'https://www.monicals.com/locations/monicals-pizza-of-st-joseph/', 'http://www.steveedaniellehairandmakeup.com/', 'http://www.myhomegroup.com', 'http://all4you.cleaning', None, 'http://www.drkennedychiro.com', 'https://www.petsmart.com/stores/us/az/surprise-store1040.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', '1592174651', 'http://www.moestire.com', 'http://theartpartystudio.com/', 'https://www.handandstone.ca/locations/richmond-hill', 'http://www.smallcakesphx.com', 'http://www.ratatouillerestaurante.com', 'https://rosyeyebrows.com', 'http://www.phoenixcylinderhead.com', 'http://www.gobencars.com/', 'http://www.bellamiahairstudio.com/', 'https://www.hotelartskensington.com', 'http://www.qimontessori.com', 'http://www.AZbodySugaring.com', 'https://www.ceenta.com', 'https://www.firehousesubs.com/locations/nc/indian-trail', None, 'http://startersaz.com', None, None, 'http://pdubsbbqlasvegas.mypub.website', 'http://porterchiropracticaz.net', 'http://www.alexanderslv.com/', '1592174720', 'http://www.milestonesrestaurants.com/', 'http://www.eddiesalehouse.com/', None, 'http://www.xclusivesparlor.com/', 'http://www.christianjamesart.com/#!/page/183244/home', 'https://www.wyndhamhotels.com/hotel/49487?tel=18002521709&iata=00093785&cid=fe:ra:20170406:yl:pp:ramus:49487', 'http://www.torontomarriagecounselling.ca', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.asianimages.biz', 'http://www.sallybeauty.com', 'https://www.jeansflowers.org/?srccode=yelp_track', 'http://www.lassendasspineinstitute.com', None, 'https://locations.jackinthebox.com/us/az/chandler/900-n-cooper-rd', None, 'http://www.caplans.ca/', None, None, 'https://www.ewingirrigation.com', 'http://www.six02.com/scottsdale', None, None, None, 'https://internetmarketingteam.com', 'http://lucerestaurant.net', 'http://www.penn-station.com/', '1592174806', 'http://loandaodentistry.com', '1592174812', None, None, 'https://bmcmattress.com?utm_campaign=PhoenixJanMar2018&utm_medium=organic&utm_source=Yelp&utm_content=website-organic', 'http://www.homesurfacesaz.com/', 'http://thelivingroomhairstudio.com', 'http://www.lecreuset.com/stores/tanger-outlets-phoenix-glendale-az', 'http://clinicalsolutionsskincare.com', 'http://www.danier.com', 'http://www.hollisfamdental.com', 'https://drivingmba.com/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Yelp-Ads', 'https://genkijapanese.info', 'http://www.contactlensking.com/', 'http://www.head2toessalon.com', None, None, None, 'http://americarestaurant.ca/', None, 'http://www.amresupply.com/locations/calgary', None, None, 'https://dekalash.com/find-a-studio/pennsylvania/wexford/', None, 'https://www.mjchristensen.com', 'http://www.pusateris.com', 'http://ProCS.us', 'http://swandetailing.com', 'https://ironglovesboxing.com/', 'http://www.bellunionautoservice.com', 'http://www.shoepalace.com?utm_source=yelp&utm_medium=yelp149', 'https://axethrowingpgh.com/booksouthhills/', 'http://www.tuttifruttidejeuners.com/en', 'https://www.courtesyjeepsuperstitionsprings.com', None, 'http://www.londoncleaners.com', None, 'http://www.helvighealth.com/', 'http://www.bebe.com', '1592174941', 'http://www.verizonwireless.com/stores/arizona/scottsdale/promenade-330170/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.lilliputhats.com/', 'https://www.number7honda.com', None, None, 'http://www.wineamplified.com/', 'http://www.glennstoolservice.com', 'http://www.thevictorianmonkey.com', None, 'https://fntarizona.com/scottsdale-kierland', None, 'http://www.anthemchildcare.com', 'http://www.nicols.ca/', 'http://blueskyoils.com', None, 'http://faceofanangel.net', 'http://www.intersport.ca', 'http://shessheik.com', None, None, None, None, 'http://www.adventcoworking.com', 'https://www.walmart.com/store/2512/phoenix-az/details', 'http://www.universalmotorcarslv.com', 'http://northpawdogs.com', '1592175027', 'http://www.pawsinthebath.com', 'http://www.auntieannes.com', 'https://www.walmart.com/store/2256/henderson-nc/whats-new', None, None, None, None, 'http://www.scavolinitoronto.com', 'http://holidaypetfestival.com', 'http://www.precisealterations.com', None, '1592175060', '1592175063', None, None, None, 'http://cateringcompanieslasvegas.com', 'https://www.wyndhamhotels.com/hotel/09499?tel=18003291073&iata=00065402&cid=fe:di:20161220:yl:pp:dius:09499', None, 'http://www.samosagrill.com/', 'http://www.lvcrystalnailspa.com', 'http://www.jamesgallery.net', None, None, 'http://www.thekentstage.com', None, 'http://noirtacgroup.com', 'https://www.goodyearmoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://yuriyscustomjewelry.com', None, 'http://www.vdevmaison.com', 'http://www.newprairieconstruction.com', 'http://www.parkroadhealingarts.com/', 'https://www.ecolinewindows.ca/location/calgary/', None, 'https://www.target.com/sl/mesa-west/1429', None, None, None, None, None, 'http://www.peterparvez.ca', None, 'http://www.teavana.com', 'http://www.lifecaremedicalrx.com', 'http://www.saladessensations.com', 'https://www.jerseymikes.com/3020', 'https://www.uneedmartialarts.com', '1592175182', 'http://aldi.us/index_ENU_HTML.htm', 'http://lincolndoor.com', 'http://bk.com/', None, None, 'http://designerartdirect.com', 'http://www.eljesseautorepair.com/', '1592175206', 'http://www.marriott.com/hotels/travel/yyzbp-fairfield-inn-and-suites-toronto-brampton', 'https://bolmergc.com', 'http://www.snapfitness.com', 'http://www.arrowheadlakesdentistry.com', 'http://www.simonesmtlebanon.com', 'http://www.jewelrysalonlv.com', 'http://www.whitehousechicken.com', 'http://www.carlitosmokes.com', None, None, 'http://www.riderscycleboard.com', None, None, 'http://www.conns.com/store-locator/nevada/las-vegas-89121', 'http://www.glowbeautyloungellc.com', None, 'http://www.sugarmarmalade.com/', None, None, None, None, 'http://scottsdalelavishnails.com/', 'http://www.bambooandspine.com', 'http://www.eyeglass-store.com', 'http://www.pioneercardiovascular.com', 'http://www.davisvillemedicalclinic.com', None, 'http://www.robbellplumbingservices.com', None, None, 'https://oralsurgerylv.com', 'http://www.ritzcarlton.com/en/Properties/Phoenix/Dining/Bistro24/Default.htm', None, None, 'http://envynailsspa.ca', 'https://happytreeslandscaping.com', None, None, None, 'http://kimmiesrestaurant.com', 'http://www.7thdegreeclothing.com', None, None, 'http://www.168sushibuffet.com/mississauga', 'http://www.chipofftheblocklv.com', None, 'http://www.ezpawn.com', 'http://www.applebees.com', 'http://www.portofsubs.com', 'http://www.thecharlotteforum.com', 'https://lastresrosasllc.yahoosites.com', 'http://www.amayaexpress.com/', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Phoenix-AZ-85023/858021/', None, '1592175367', 'https://agents.farmers.com/nv/las-vegas/yebel-escalona?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://buddysautorepair.com', 'http://www.mactechcomputer.com', 'http://www.azmountainviewmassage.com', 'http://vandykeaesthetics.com', None, 'http://www.faithfulwordbaptist.org', None, 'http://www.calgarylabservices.com/', 'http://onestoprealtylv.com', 'http://farmhousefoods.com/', None, None, 'http://koreangrillhouse.com/yonge-bloor-location/', 'http://rollinrustgarage.com', None, 'http://vintageconservatory.com', 'http://phatbuddhatattoos.com', 'https://www.241pizza.com', 'http://www.DentistryoftheCarolinas.com', None, 'http://www.rockstaraccountantsllc.com', 'http://www.chandleraz.gov/default.aspx?pageid=625', None, 'http://www.onemanandahammer.com', None, 'http://www.sushinotori.com', '1592175450', 'http://locations.harristeeter.com/nc/charlotte/205/', None, 'http://www.scriptpharmacy.ca/', 'http://www.pancheros.com/locations/urbana', 'http://www.cultivategoods.com', 'http://www.starbucks.com', 'http://www.reynoldsplumbingllc.com/', 'http://www.clevelandcupcakecompany.com/', 'http://www.esmil.com', 'https://www.destinationhotels.com/scottsdale-resort/dining/bar-six40', 'https://www.wwwilliams.com/location/phoenix-az/', None, 'http://www.quiktrip.com', '1592175489', 'http://paradisegreens.com', 'http://www.aerobatics.com', None, None, None, 'http://bellybombz.com/lasvegas', None, 'http://www.madtownrentals.com/', 'http://www.eyedistrictbyjo.com', 'https://www.bathandbodyworks.com/store-locator', None, 'https://www.zamzamhalalmeat.com', 'http://www.walmart.ca/en/walmart-meadowvale-supercentre/3054', None, None, 'http://www.perfectcredit60days.com', 'http://todaysauto.ca', None, None, None, 'http://stores.tuesdaymorning.com/nc/matthews/home-decor-matthews-nc-char0146.html', None, None, 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', None, 'http://www.tntwindowtint.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://galaxyktv88.com', 'http://www.hollandmarshsoupfest.ca/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.cellularsourcestore.com', 'http://aldi.us/index_ENU_HTML.htm', 'http://www.openstudioartcafe.com', None, None, '1592175611', 'http://www.haifengchinese.com', 'http://www.centennialpediatricslv.com', None, None, 'http://www.mississauga.ca/portal/discover/lakeviewgolf', 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'http://www.abceurodeli.com/', None, '1592175639', None, 'http://www.malkinlegal.com', 'http://www.nextlevelpaintersaz.com', None, None, None, '1592175656', 'https://www.centurylink.com', None, 'https://www.mytightface.com', None, 'http://www.suncoastaz.com/', 'https://www.indochino.com/showroom/charlotte', None, 'http://www.indulgeandco.com', None, 'http://tradeandlore.com', None, 'http://heartlandgsbeautybar.simplybook.me/sheduler/manage', 'https://www.emser.com', 'http://www.quiktrip.com/', None, 'https://www.smithsfoodanddrug.com/storeHours?store=70600376', None, 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', '1592175713', 'http://www.The-Dawg.com', 'http://www.southtempeapartments.com', 'http://shop.hobbylobby.com', 'http://www.thefitalterations.com', 'http://www.vpicasso.com', None, 'http://www.healingheartspeds.com/', 'http://sportsperformanceandspine.com', 'http://www.racewaychrysler.com', 'http://www.fendi.com/ii/store-locator', 'http://clickserve.dartsearch.net/link/click?lid=43700044280205718&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', '1592175749', 'http://www.barbqueboss.com', 'http://adjaafricanbraiding.com', '1592175758', 'http://beyondexpectationdental.com', None, 'http://www.petvethospitals.ca', 'http://www.azenaphoto.com', 'http://www.axisgear.ca', 'https://www.trebilcockcoffee.ca', 'https://www.thetouchofitaly.com', 'http://Rickslawnandlandscaping-lv.com', '1592175785', 'http://www.onceuponachildmacleod.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.espressoroyale.com/', 'http://dtrschooloftrucking.com', 'http://newoutlookopticalnv.com', None, 'http://sushi930.com', 'https://www.mediweightloss.com/locations/ballantyne?_ppc=Z8FWKRXKT5', None, 'http://www.richardsgardencenter.com', None, 'https://locations.levi.com/nc/charlotte/denim_charlotte_nc_258.html', 'http://mojoscoffeeandmore.com', 'http://www.barefootpoolman.com', 'http://www.lushexpress.com', None, 'http://www.stclair.org', None, '1592175848', 'http://www.palmettopethospital.com', 'http://www.mountainsidechiropractic.com', 'http://www.exclusiveballoons.com', 'https://diamondsstrip.ca', 'http://valleywidehouses.com', None, 'http://www.dayspring-umc.org', None, 'https://www.northtownvethospital.com', None, 'http://www.candy-addict.com', 'http://www.harthouse.ca', 'http://www.elitephoenixseo.com/', None, 'http://shea-blvd-chiropractor.com/', 'http://www.alluniformwear.com', None, 'http://www.draskovich.com', None, 'https://lvcollectables.com', 'http://jonesmoverz.com', None, 'http://www.gobeautybar.com', None, 'http://calgary.regency.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_calrc_en_homepage_desktop&code=YB', None, None, 'http://www.thesundanceclinic.com/', 'http://www.sunvalleyfamilyoptometry.com', 'http://www.vipbeautysalon.org', 'http://www.murdockmeals.com', None, 'http://www.pghfilmmakers.org', 'http://pferguson.pillartopost.com', None, 'http://www.dunkindonuts.com', None, None, None, None, 'http://www.masterpieceescapes.com', 'https://nothingbundtcakes.com/bakery/AZ/goodyear?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=goodyear_138', 'http://www.bobbiepinbeauty.com', 'http://www.firkinpubs.com', 'http://murphyusa.com', 'http://Swanpizza.com', 'http://www.advancedpreventivemedicine.com/', 'http://www.starbucks.com/store/6597/', 'http://www.infinityhd.tv', 'http://www.starbucks.ca', 'http://www.lasvegashomewatchers.com', 'http://torontopawn.ca', '1592179247', 'http://www.vegasdiscountnutrition.net', 'http://www.bulkbarn.ca/en-ca/index.html', 'http://adventuredogpark.com', 'http://www.timhortons.com/ca/en', 'http://www.apple.com/retail/southpark', 'http://www.iltartufo.ca', 'http://www.hydrotherapiesplus.com/', 'http://www.desertspringschiro.com', 'https://www.pizzahut.ca/store-details/store-R42101/pizza-hut-Etobicoke', 'http://www.thetirexpress.com', 'http://www.tuckedawaycraftkitchen.com', 'http://www.renewedlifechiropractic.com', 'http://www.phxplastering.com', None, None, 'http://www.muchoburrito.com', 'http://www.theriverwoodconservancy.org/', None, None, None, 'http://blackforgecoffee.com', 'https://www.slatescottsdaleapartments.com/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://locations.dennys.ca/AB/CALGARY/248179', None, 'http://www.babysafehomes.com/united-states-baby-proofing-locations/child-proofing-phoenix-arizona', 'http://www.clevelandmoto.com', 'http://www.applerepaircanada.ca', 'https://www.druryhotels.com', 'http://www.sabaiaz.com', None, 'http://www.sunsationalswimschool.com/', 'http://www.lapetgrooming.com', 'http://www.gamestop.com/store/us/az/scottsdale/2760/sonoran-village-gamestop', None, 'http://www.ezyes-takeout.com', None, 'http://www.trendvape.com', 'https://glassnickelpizza.com/location/sun-prairie/', 'http://www.arizonarvresorts.com/Pioneer', None, '1592179997', 'http://www.myhealingplaceaz.com', None, 'http://www.restaurantconfluence.com', None, 'http://www.bioprollc.com/', 'http://www.valleyofthesunpharmacy.com', 'http://www.arizonasandwichco.com', None, 'http://www.frogbox.com/toronto', 'https://sushisanrestaurant.business.site', 'http://www.jwoodflooring.com', 'https://www.lefrancisstudios.com', 'http://www.aboutudental.com', 'http://www.kokomogrills.com', 'http://www.ivanhairsalon.ca', '1592180030', None, 'http://www.granadalakestempe.com', 'http://www.capellaeyecare.com', None, None, 'http://www.onthelistdenver.com', None, 'https://www.lvscc.com/south-rancho', 'http://www.lotsmartsolarscreens.com', 'http://www.ontariotrails.on.ca/trails/view/cheltenham-hills', 'http://georgesbrasserie.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://freshandeasy.com/', None, None, 'http://www.northwoodslanes.com', 'http://cleanmycarpetlv.com', 'http://www.nonnispizzamenu.com', None, 'http://globalbikes.info/', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', '1592180077', None, '1592180081', 'http://www.hotdogonastick.com', None, 'http://www.luchitas.net/elyria.php', None, None, None, 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', None, None, 'https://www.fitnessworks.com/locations/dobson-rd-chandler-blvd', None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.buckysportabletoilets.com', None, None, 'https://www.mirage.com/en/restaurants/osteria-costa.html', 'https://www.cheyennedentalgroup.com/?utm_source=yelp&utm_medium=link&utm_campaign=yelp', 'http://www.atobmove.com', 'https://locations.waxcenter.com/nc/charlotte/charlotte-arboretum-0169.html', None, None, 'http://www.phoenixpubliclibrary.org/Locations/Pages/Yucca.aspx', None, None, 'http://www.qsdiner.com', 'http://www.pb.com', 'http://www.amenzone.com', 'http://www.cremacoffee.ca', 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpsouthwestorganic', 'http://www.blueberryhillrestaurants.com/', 'http://www.wishacake.ca', 'http://www.littlecrittersvet.com', 'http://www.c3lasvegas.com', '1592180154', None, 'https://www.thebrick.com/pages/store-north-york', 'http://www.rightc3.com', 'http://imboardgames.com', 'http://www.bwilliamsdds.com', 'http://www.stephita.com/', 'http://www.underdogpetrescue.org', 'http://www.canadianamphitheatre.net/', 'http://www.anthropologie.com', 'http://www.noblecare.us/', None, None, 'http://titanhomeimprovements.com', 'http://nvjawdoc.com/', 'https://www.redlobster.ca/locations/list/on/brampton/368-queen-street-e', '1592180189', None, 'http://www.scottsdale-sc.com', 'http://www.zappos.com', 'http://www.naturalgourmetfoods.com/', 'http://www.walgreens.com/locator/Walgreens-10503-W-Thunderbird%2C-Suite-101B-Sun-City-AZ-85351/id=10018', None, '1592180205', 'http://www.pittsburghcitywide.com', None, 'http://www.inspectioneeringpgh.com/', 'http://www.arizonacharliesboulder.com/Food-Drink/Sourdough-Cafe', 'http://www.regency.edu/campus/madison/?guest', None, 'https://www.leprovencalbistro.com', '1592180219', 'http://www.fallasstores.com', None, 'http://sabiskitchen.com/', 'https://www.nofrills.ca/store-locator/Enzo%27s+nofrills+%28Yonge+St.%29/0770?storeId=0770', 'http://www.sassiskin.com', '1592180232', None, 'http://www.kyrene.org', 'https://www.aqualineplumberselectriciansacrepairscottsdaleaz.com', None, '1592180244', None, None, 'https://bananarepublic.gap.com', 'http://www.artisticintegrity.ca', 'http://www.plumberphoenixboydco.com', '1592180257', 'http://www.goldengeckocoffee.com', None, 'https://www.kfc.ca/store/3199-blvd-taschereau-greenfiled-pk', 'http://www.carolynannryan.com', 'http://www.hyperproductionsdjs.com', 'http://www.menchies.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.coldstonecreamery.com/stores/20030', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.globalpetfoods.com', 'https://www.nbc.ca', None, 'https://www.maids.com/106/?utm_source=Yelp', 'http://www.preferredhomecare.com/', 'http://www.lighthouseNMT.com', None, 'http://www.coiffeurssalon.com', None, 'http://www.ganleywestsidehyundai.com', 'http://www.marcsimonlaw.com', None, 'https://www.lamaithaicuisineaz.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=1943&localechange=1', None, 'http://www.currentdentallasvegas.com', 'http://www.coupebizzarre.com', None, 'http://hallfamilyfarm.com/', 'http://www.ohiyo68.com', 'http://www.knuckleheadstobacco.com', 'https://www.livingspaces.com/stores/phoenix', None, 'http://aldi.us/index_ENU_HTML.htm', 'https://www.prestigecleaners.com', '1592180331', 'http://www.allwashedwindowcleaning.com', 'http://www.chiropractichealthmatthews.com/', 'https://www.phxrisingfc.com/stadium-information', 'https://www.ritasice.com', 'http://logansroadhouse.com', 'http://bluetruckwindowcleaning.com', 'https://restaurants.applebees.com/az/tempe-88083.html?utm_campaign=Local&utm_medium=Display&utm_source=Yelp', 'http://moonlitetavern.com', 'http://www.fiveguys.com', None, 'http://www.HealthyOutlookFamilyMedicine.com', 'http://www.fresh52.com', 'http://www.meckneurology.com', 'https://www.erieinsurance.com/about-us/locations/charlotte', 'https://www.rosewoodcandlebar.com', 'http://www.lvzendog.com', None, 'http://www.centralazsupply.com', 'http://www.costco.com/warehouse-locations/henderson-nv-673.html', 'http://www.coldstonecreamery.com/stores/20030', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, None, 'https://www.revampextensions.com', 'https://breezemassage.wixsite.com/85301', 'http://www.costcutters.com', None, 'http://www.rodefshalom.org', 'http://www.haychiro.com', None, 'http://www.nailsupspahuntersville.com', 'http://fountainhillsbowling.com', '1592180403', 'http://azmrfixit.com/', 'https://probateattorneyvegas.com', 'http://www.siegelsuites.com/rent-apartment-las-vegas/paradise-las-vegas-apartments.php', None, None, 'http://www.shopthemensroom.com', None, None, '1592180420', 'http://www.lilbaci.com', 'http://www.toronto.ca/parks/prd/facilities/complex/1099/index.htm', None, None, 'https://ezautosaleslv.com', 'http://www.dmscshea.com', 'https://haircutmenbillgreenpittsburghpa.com', 'http://www.dentalcaretoronto.com', None, None, '1592180441', 'http://www.mirrorbombstudio.com', 'http://www.2020visionphotos.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YULMV', None, 'https://www.tgifridays.com/locations/1110/fridays-robinson-pennsylvania', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZTS', 'http://www.annalakshmi.ca', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://lvcraftshows.com', None, 'http://ktran1401.wix.com/pamperednailsalon', None, None, 'http://www.poolman.com', 'https://www.travelex.com/stores/phoenix-sky-harbour-international-airport-terminal-4-checkpoint-b-phoenix-az/7283', None, 'http://oldnavy.gap.com/customerService/store.do?storeid=6528', None, None, 'https://www.cantina15eleven.com', None, None, 'http://locations.truereligion.com/az/scottsdale/51049/', 'http://www.nolldentistry.com', 'http://www.annexales.com', 'http://dekra.us/en/nevada/las-vegas-6020-n-decatur-blvd/', 'http://www.swanksalon.info', 'https://visionsource-loepervisionteam.com', 'http://hoopssportsbar.com', 'http://www.ArgonPest.com', None, None, None, 'http://www.arizonainterlocks.com/tempe', 'http://www.MellonsPub.com', 'http://arichtreatments.com', 'http://www.deserttailsanimalclinic.com', 'http://www.billsbarandburger.com/venues/pittsburgh/', '1592180530', 'http://www.hcxcharlotte.com/carmel-commons-hair-salon/', 'https://bignons.com/s-tryon-location', '1592180537', 'https://nothingbundtcakes.com/bakery/NC/charlotte?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=charlotte_145', None, 'https://stjudesranch.org/', 'http://www.graciebarra.com/phoenix-az', 'https://www.outback.com/locations/oh/cuyahoga-falls', 'http://www.pizzapizza.ca', 'http://www.eatatfellinis.com/', 'http://www.santurbanospa.com', 'http://www.theartofshaving.com', None, None, 'http://www.sugarpeony.com', 'https://www.lifecelebrationpetcrematory.com', 'http://www.hassanphoto.com', 'https://www.littlejohnslawns.com/', 'http://www.tiptoptrough.com', None, None, None, 'https://www.sephora.com/happening/stores/pittsburgh-shadyside', 'http://clevelandcinemas.com/location/6347/Chagrin-Cinemas-Showtimes', 'http://www.lifetimeeyecarecenter.net', None, '1592180585', 'http://www.wetseal.com', 'http://www4.ncsu.edu/~jtdemars/theshakeshack.html/', 'http://www.usfries.com/', 'https://www.carx.com/madison/5633-odana-rd/', 'http://www.ihg.com/staybridge/hotels/us/en/madison/msnhc/hoteldetail', 'https://siennajewelsalon.com', 'https://andersonsdelivery.com', 'http://www.azwood.com/', None, '1592180608', 'https://www.sunbaraz.com', 'http://www.splishsplashpools.com', 'http://www.swisschalet.com', 'http://www.hutchsbicyclegarage.com', None, 'https://www.levinfurniture.com/furniture-store/oh/solon/6130-kruse-drive', 'http://waternicetempe.com', 'http://lafontanagelati.com/', None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-jomax?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-jomax', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', '1592180634', 'http://www.mezes.com', 'https://www.crystalglass.ca/location/calgary-south', None, None, 'http://bikebarnaz.com/', None, None, 'http://www.tashabradyphotography.com', None, 'http://www.sunrisecarpetupholsterycleaning.com/', '1592180654', 'http://www.geniecarwash.com', 'http://www.phoenixlocksmithoncall.com', 'http://www.bronzfx.com', None, 'http://www.urbancurls416.com', 'http://www.einsteinbros.com/', 'https://www.chick-fil-a.com/surprisemarketplace', None, 'http://www.andrewblairs.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.caferio.com/', 'http://spencerstv.com', 'http://www.cuttlefishscottsdale.com/', 'https://www.terragreenhouses.com/terra-milton-garden-centre', 'http://www.performanceext.com', None, None, 'http://charlottenc.gov/cats/rail/lynx-blue-line/Pages/parkwood-station.aspx', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.cinemark.com/nevada/century-16-south-point-and-xd', 'http://www.bgchenderson.org', 'http://popeyeschicken.ca', None, 'http://www.shanghaiwokbyby.com', 'https://www.phoenixmechanicshop.com', 'http://www.mysichuanpalace.com', None, 'http://www.lowes.com', 'http://www.extremepestcontrolLasVegas.com', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', None, 'http://www.sidernobakeryllc.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://www.wolbertautobody.com', 'http://www.mscarolsgymkids.com', None, 'https://www.redlobster.com/locations/list/nc/concord/8012-concord-mills-blvd', 'http://www.crazydaisieslv.com', 'http://abbeyroseflorist.com', 'https://positive-movement-logistics.business.site', 'http://www.delaneyauction.com', None, 'http://www.freakstattooemporiumnv.com', 'https://www.oxifresh.com/locations/nc/charlotte-carpet-cleaning/?utm_source=yelp&utm_medium=social&promo_code=YP5000', None, None, None, 'http://www.alnoorkebab.com', None, 'http://www.avalondentistry.ca/', 'http://jwoodsonderm.com', None, None, 'http://www.palmcleaningsystems.com/wp/', None, None, None, 'http://www.innovativevapors.com', 'http://www.naturalbeautyhairboutique.com', 'http://www.bethelbarbershop.com', 'http://www.livescanlasvegas.com', None, 'https://hotelxtoronto.com/en/falcon-skybar.html', 'http://www.danielsdiscount.com', 'http://www.thesmilecreators.com', None, None, None, None, 'http://www.koolthairestaurant.com', None, None, 'http://www.cowboycooling.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', '1592180808', 'http://www.jimpeplinski.ca', 'https://www.avis.ca/car-rental/location/CAU/CA/PQ/Dollard-des-Ormeaux/PCQ', 'http://www.vasilis-yyc.com', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.avecpanacherestaurant.com', 'http://www.shell.com', 'https://www.creativekidslearningcenter.com/schools/las-vegas-nv-6705/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhancedprofile', None, None, '1592180834', 'http://www.eatrastapasta.ca', 'http://www.chmuseums.org', 'http://www.settlersridgepa.com/', 'http://www.rightgear.net', 'http://www.bodyrevolution.net', 'https://istanbulsofra.com', 'http://www.3riversartsfest.org/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/32331+North+Scottsdale+Road-Scottsdale-AZ-85262/storeid=7839?cid=ps_ylp_2020', None, None, 'http://www.nvcoin.com', 'http://specialtyrvaz.com', 'http://www.azultimatechiropractic.com', 'http://www.moldanddefectlawyer.com', None, 'http://www.ultrasmoothskin.com/', 'http://www.tbmelectriclasvegas.com/', None, None, None, 'http://www.imperialpalace.com/casinos/imperial-palace/restaurants-dining/ginseng-3-detail.html', 'http://www.ventureoutrvresort.com', None, None, 'http://smittysresidentialpainting.com', 'http://royalthaihakka.com', 'http://www.instantac.com', None, 'http://www.rawfitnesslv.com/summerlin.html', 'https://calgarymovers.net', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89084/600-in-north-las-vegas/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-600&utm_content=website-link&howheard=IYE', None, None, 'http://www.cobrinhabjjlasvegas.com', 'http://www.rooterranger.com', 'https://www.ladym.com', 'http://www.doubledouble.ca', 'http://www.orleanscasino.com/entertain/bourbon-street-cabaret?disid=wmm_yelp_to_corporate_bourbonstreetcabaret_organiclink', None, 'http://pawncorp.com', '1592180934', 'http://www.visionexpress.ca', 'http://www.mashawiaz.com/', 'https://www.pearsoneyecare.com/location/superstition-springs-mall-mesa/', 'https://trivenisupermarket.com', 'https://leader-barber-style-shop.business.site', 'http://www.unclesmoke.com', None, 'https://www.lasvegasbouquet.com', None, 'http://sachisalon.com', 'http://www.bixelsstudios.com', 'http://www.hairsalonlulu.com', None, 'http://www.thriftypropane.com/', 'http://www.balloonatix.com', None, None, 'http://www.starbucks.com/store/9298/', 'http://mississaugaemission.ca', 'http://www.dirtyat1230.com', None, 'http://www.11BravoMobileAuto.com', 'http://www.lagoeastbank.com', None, 'http://www.vitabellasalonandspa.com/', None, 'http://www.climatechangeyyc.com', 'http://fingerprintingink.com', 'http://www.oudejansinteriors.com', None, 'http://www.japco.ca', None, '1592181015', 'http://www.explace.on.ca', 'http://www.kensautorepair-hub.com', 'https://shop.nordstrom.com/store-details/nordstrom-scottsdale-fashion-square?utm_source=yelp&utm_medium=organic&utm_campaign=fls&utm_content=380&utm_channel=lcl_brand_p&sp_source=yelp&sp_campaign=fls', 'http://www.sfagentonline.com?cmpid=FVUJ_BLM_0006', None, 'https://www.aqua-tots.com/ahwatukee/', 'https://myhoneybakedstore.com/charlotte/114', None, 'http://phoenix.gov/parks', None, None, None, 'http://www.dryaged.ca', None, 'http://www.cpk.com/Location/Details/Ross-Park', None, 'http://www.chavezboxinggym.com', 'http://www.curvyconsignments.com', None, None, 'http://www.swlegalgrp.com/', None, None, 'http://www.superstore.ca', None, 'http://www.luxor.com/amenities/amenities_the_spa.aspx', 'http://chucksroadhouse.com', None, None, 'https://www.restaurant-mesa.com', 'http://www.gap.com/products/westlake-oh-store-7181.jsp', 'http://www.gotitcoverednv.com', None, 'http://www.ihg.com/holidayinnexpress/hotels/us/en/mentor/mntoh/hoteldetail', None, None, None, None, 'http://nanadeesdiner.com', 'http://shopping.schubachstore.com/', None, None, 'https://aarons-ark-mobile-veterinary-services.business.site', None, 'http://www.eldoradocasino.com/dining.cfm', 'http://www.commutehome.com/', None, 'http://www.badgergymnastics.com', 'http://www.hightvet.com', None, 'https://www.wedgewoodweddings.com/venues/arizona/palm-valley?utm_source=yelp&utm_medium=social&utm_campaign=palm-valley-yelp', 'http://Inglewoodpizza.ca', 'http://www.gianteagle.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.boulangerielefournil.com/', 'https://www.walmart.com/store/4148/charlotte-nc/details', 'http://www.byrdspub.com', None, 'http://www.headwaystudio.com', 'http://www.bronzecafe.com', None, 'https://druxys.com/location/2-st-clair-ave-colonia-place/', 'https://www.choicehotels.com/arizona/phoenix/sleep-inn-hotels/az140/rates', 'http://www.alcornhair.com', 'http://www.topshotlasvegas.com', None, 'http://www.bigmouthluckdumplinghouse.com/', 'http://www.matsudasushi.com/', None, '1592181177', 'http://nile-seafood-market-restaurant.business.site', 'http://versatileautoappearance.com', 'http://www.pizzahut.com/', 'http://www.walmart.ca/en/richmond-hill-supercentre/3195', None, 'https://attorneysforfreedom.com', 'https://havensmedispa.com', 'http://www.bannerhealth.com/locations/glendale/banner-physical-therapy-eugie?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', 'http://www.allproawninglv.com', None, 'http://www.woodbinetoyota.ca', None, 'http://www.ihg.com/holidayinnexpress/hotels/us/en/calgary/yyccg/hoteldetail', 'https://sukiesbridal.com', None, 'http://green-pepper-ot-xanh-asian-cuisine.business.site', 'http://www.sodadispenserdepot.com', 'http://www.7-eleven.com/?yelp=36121', 'http://www.medusaslv.com', 'http://www.cozzeria-pizzeria.com', 'https://www.alanhuirealty.com', 'http://www.clevelanderbar.com/', 'http://www.streamersicecream.com/', 'http://www.fraziersbarbershop.com', None, 'http://www.mufflermasters.com', None, 'https://functionbar.ca', 'http://worldsalon.ca', 'http://www.PetLossAtHome.com', 'http://www.summerlindance.com/', 'http://voxcurvy.com', 'http://www.paintingbyhector.com', None, None, 'https://marsautoservice.net', 'https://www.wyndhamhotels.com/hotel/08797?tel=18007606483&iata=00093785&cid=fe:tl:20170523:yl:pp:tlus:08797', None, 'https://locations.paychex.com/us/pennsylvania/pittsburgh', 'http://www.ymcacharlotte.org', 'https://www.chandlerair.com', 'http://www.poshmommy.ca', '1592181276', None, 'http://www.beancurd.biz', 'http://hummusfactorylv.com', 'http://gilberttowncommons.com/?utm_campaign=YelpWebsite&utm_medium=YelpBusinessProfile&utm_source=Yelp', 'http://www.starloancenters.com', 'http://www.pnc.com', 'http://skincarecleveland.com/index.html', None, 'https://www.kalologie-lasvegas.com', None, None, 'http://www.westlibertycycles.com', 'http://www.marriott.com/hotels/travel/phxcs-springhill-suites-phoenix-chandler-fashion-center/', 'http://Chagrin-Falls.certapro.com/?source=Yelp', 'http://www.keepitcut.com', 'https://www.lugayfamilydental.com', 'http://k-momo.com', 'http://www.executivelounges.com', 'http://www.trulyengravables.com', 'http://www.ecodryrestoration.com', 'https://www.target.com/sl/arcadia-crossing/950', 'http://www.hobbylobby.com', 'http://www.hubnest.com/', 'http://fandombar.com', None, None, None, 'http://www.gianteagle.com', 'https://www.lasvegas-propertymanagement.com', 'http://www.boxheartgallery.com', 'http://corneaaz.com', 'http://www.aveda.com', 'http://www.dralbertli.com', 'http://www.thegatewaybarandgrill.com/', 'http://www.meckabc.com', None, 'http://sugarshackrecords.net', 'http://www.starbucks.com/store/89998/ca/vmr-lucerne/2362-chemin-lucerne-ville-mont-royal-qc-h3r-2k5', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', 'http://www.bennysbar.net', 'http://www.ringaudio.com', None, 'http://dlautomotive.com', 'http://401dixieinfiniti.ca/', 'http://www.operationhalloween.com', 'http://www.fetchpetcare.com', 'http://bluebirdcarpet.com', 'http://auclv.vegas', 'http://www.coachcanada.com/coachcanada/ss.casino.asp', 'http://www.novellenail.com', None, 'https://ad.doubleclick.net/ddm/clk/414776926;215768644;y', 'https://www.apexskin.com/locations/solon-oh-dermatology-office/', 'https://vyiannibas.wixsite.com/juliana', '1592181407', None, 'https://ca.louisvuitton.com/fra-ca/magasin/canada/louis-vuitton-montreal-ogilvy?campaign=b_yelp/storepage', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700007898397760&ds_s_kwgid=58700000649767852&ds_e_adid=%7Bcreative%7D&ds_url_v=2&cmpid=ADV_PG_%5B*KeywordID*%5D', 'https://Scottsdalequarter.com', 'http://www.healthpalace.ca', 'http://www.aamcogilbertchandler.com', None, 'https://www.hungryhowies.com/store/hungry-howies-01823?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=1823&utm_content=Website_Link', None, 'http://www.generate.to', None, 'http://campagnolotoronto.com/', '1592181442', 'https://www.24hourfitness.com/gyms/las-vegas-nv/silverado-las-vegas-sport', 'http://www.captainscovenc.net/', 'http://sanctuaryongreen.com/', 'http://www.nulawn.net', 'https://www.simonmed.com/locations/all/simonmed_imaging___greenfield', None, None, None, 'http://www.papajohns.com', None, 'http://restaurantgalleria.ca/fr/', None, 'http://www.sbcfoods.com/', 'https://freshfixofheights.com', 'http://www.myautoamerica.com', None, 'http://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEEM', 'http://www.fonda-las-cazuelas.com', 'http://zaxe.ca', 'http://www.jmphoenixcriminalattorney.com/', None, 'http://www.aztrailstravel.com', 'http://www.allstartaxi.ca', 'http://www.autobell.com/ab_locations/333-n-new-hope-rd/', 'https://stopandshop.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.bergamotmassage.com', 'http://rossispizzamonona.com/', 'http://www.lakeeriemonsters.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89128/027192/', 'http://go.georgestreetphoto.com/l/9752/2014-06-04/m1c3t', None, 'http://www.danspoolcare.com', 'http://www.earlycollegenv.com', 'https://www.oliversplumbing.com', 'https://www.lowes.com/store/AZ-Surprise/1607?cm_mmc=YEXT-_-SiteLink-_-1607-_-Lowes', 'https://stores.guitarcenter.com/avondale?source=4GOA5AJBB', 'https://www.perfectteeth.com/office/az/surprise/85379/waddell/', 'http://www.conciergemakeup.com', None, 'http://soilextractors.com', 'http://greengarageaz.com', '1592181555', None, 'https://www.apparelprousa.com', None, 'http://www.adamahmadison.com', None, None, 'http://www.dieselworldwide.ca', 'http://heritagetattoolv.com', None, 'http://www.phoeniximprovfestival.com', None, 'https://www.cosmeticlasercenters.com', None, 'http://www.zapitwash.com', 'http://therocksportsbarandgrille.com', 'https://www.sprint.com/storefronts/bd/sprint-phoenix-az-85037-d-4610/', None, 'http://www.taverninthehills.com', 'https://dream-cut-barber-and-stylist.business.site', None, None, 'http://www.solsticesunglasses.com/', None, None, 'http://www.patisseriefleur.com', '1592181622', 'http://locations.michaels.com/AB/CALGARY/3902/', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreID=62', 'http://www.kristenmarieweddings.com', 'https://www.eatnpark.com', 'http://www.middletonpower.com/', 'http://www.lakeviewautopartsinc.com', 'http://www.avedamontreal-lifestyle.com', 'https://www.laplazataqueria.com', 'http://discountfloorsaz.com', 'https://www.bannerhealth.com/locations/mesa/banner-urgent-care-1', 'https://www.shopfuego.com', None, 'https://www.labl.ca', None, None, 'http://www.cortezindustriesllc.com', None, 'http://www.skilletsforbreakfast.com/', None, None, 'http://lvfurnituredirect.com', 'https://www.petalsofloveflorist.com', 'https://www.aairofcharlotte.com', 'http://launchhouse.com/', None, None, 'http://www.friendlys.com/', None, 'http://american1stheating.com', 'http://chase.com', '1592181697', 'http://www.bcbg.com', 'http://www.signaturerentalsbyowner.com', 'http://www.traditionalstitches.com/', 'https://www.supercuts.com/locations/az/peoria/north-valley-power-center-haircuts-82958.html', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.mixxiemixologist.com', 'http://carolinawinesandspirits.com', None, 'http://www.altf.com', 'http://www.classiccarspa.com', None, 'https://palmbeachtan.com/locations/AZ/Tempe-East-Broadway-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'http://www.trustedepa.com', None, '1592181735', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592181744', 'https://www.activedecorating.com', 'http://www.TheWomansCenter.com', None, 'http://moderneraweddings.com', 'http://www.mrdetailohio.com', 'http://winginout.com', 'http://www.bigotires.com', 'https://superiorplay.com/dealerlocator/north-carolina/charlotte', 'http://www.bk.com', 'http://www.lasvegasvasectomy.com', 'http://www.wildbunchdesertguides.com', '1592181773', None, None, 'http://avonurgentcare.net/', None, None, 'http://www.mimiscafe.com', 'http://tenrenstea.com/start/', None, 'https://santafestation.sclv.com/gaming/sports-book?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.look-stylesociety.com', 'http://www.callsp.com', 'http://www.datadoctors.com/locations/101', 'https://cbdemporium.com', 'http://www.ledolci.com/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://www.marriott.com/hotels/hotel-information/fitness-spa-services/details/phxcb-jw-marriott-scottsdale-camelback-inn-resort-and-spa/5014642/', 'http://www.cocokala-lasvegas.com', None, None, None, '1592181829', None, 'http://www.twintranslations.com', 'http://www.target.ca', None, None, 'http://www.proximityatpapago.com/index.aspx', 'https://www.massageaddict.ca/calgary-sagehillcrossing/', 'http://www.donaldjpliner.com', None, 'http://bombatacos.com/fairlawn-oh', 'https://www.vitbeo.com', 'http://lanierparking.com/', 'http://SellWithOne.com', 'http://www.phoenixtitleloan.com/', 'https://www.eyesonhayden.com', 'http://CATCh.theater', 'http://www.goldenharboronline.com', 'https://www.kohls.com/stores/az/gilbert-621.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.nuturfofarizona.com', 'http://www.topgearcarwash.net', 'http://www.sansotei.com', None, 'https://www.walgreens.com/locator/walgreens-2324+w+war+memorial+dr-peoria-il-61614/id=6408', None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.bestbuyflooringcenter.com', 'http://www.flowerchildvintage.com/', 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', None, 'http://www.theglassguru.com/scottsdale/', 'http://www.clevelandrockgym.com', 'https://jessebrowns.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.colossalcupcakes.com', 'http://www.phoenixpediatrics.com', 'http://www.klearlykleaned.com', 'http://811kitchenbarlounge.com', 'http://www.blacklanterntattoo.com', None, 'http://www.dedicatedaudio.com', 'http://www.flipsideburger.com', None, 'http://www.teamorthodontics.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.appleone.com/?yelp_track', 'http://www.confectionarycupboard.com/', 'http://www.neworientalrecipes.com', None, None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, 'http://www.beckhamspub.com', 'http://www.7-eleven.com/?yelp=29644', 'http://www.goldentrianglebike.com', None, 'http://www.wildsagert8.com/', None, 'https://www.grifolsplasma.com/en/-/mesa-az', 'http://www.handsoncharlotte.org', 'https://blackbeardiner.com/location/las-vegas-tropicana/', 'http://www.resumerick.com', 'https://locations.davidstea.com/on-thornhill-17', 'http://www.trinitybellwoods.ca/', 'http://www.threes-company.com', None, 'http://www.braidyjewelers.com', 'https://acrirlty.com', None, 'http://popeyeschicken.ca', 'http://www.aactionmovers.com', 'http://www.lovhairbymarianne.com', 'http://www.pinklime.com', 'http://www.hanshiktaco.com/', 'http://www.littlecaesars.com/', 'https://local.firestonecompleteautocare.com/nevada/las-vegas/3770-s-maryland-parkway/', None, None, 'http://www.precisionguitaraz.com', 'http://www.elitehomeinspections.us', None, 'http://www.vantageloftslv.com/#Home', None, 'https://makeupbyalmah.business.site', 'http://www.salutelounge.ca', 'https://arizonaurologyspecialists.com/contact-scottsdale-thompson-peak', 'http://www.starbucks.com/store/11823/', 'http://www.azmobilereflash.com', 'http://www.baskinrobbins.com', None, 'http://www.fye.com', 'http://www.ampm.com', None, None, 'http://www.nygh.on.ca', 'https://sheridannurseries.com/store-locations/toronto-garden-centre/', None, 'http://www.weathervaneplayhouse.com', None, 'http://www.littleotterswim.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.ebtfloral.com/', 'https://bostonpizza.com/en/locations/sunridge.html', None, 'http://www.sayteaonbloor.com', 'http://www.anewtable.ca', 'http://www.bathurstbowlerama.com/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/109+Dabney+Drive-Henderson-NC-27536/storeid=7055?cid=ps_ylp_2020', 'http://www.lesleyscreativecakes.com', None, None, 'http://www.gandermountain.com', 'https://housedoctoraz.com', 'http://www.greatclips.com/', None, None, 'https://locations.cariboucoffee.com/az/phoenix/2080-w.-northern-ave.html', None, 'http://oriondetailing.co', 'https://business.google.com/website_shared/launch_bw.html?f=vegas-noodle-house.business.site', None, 'http://www.southernpawsanimalhospital.com', 'http://www.pnpkaz.com', 'http://www.eventprostrategies.com', 'http://www.penn-station.com/westvirginia/', '1592182138', None, 'http://www.bohme.com', 'http://www.fatzombietattoo.com', 'http://www.globalmarketretail.com', None, None, 'https://www.wyndhamhotels.com/hotel/28120?tel=18885951878&iata=00093785&cid=fe:mt:20180223:yl:pp:MTUS:28120', '1592182158', 'https://www.amctheatres.com/movie-theatres/phoenix/amc-westgate-20?utm_uid=yelp', None, 'http://Www.piedmontvets.com', 'http://www.chachago.ca', 'http://rebelluxeaz.com', 'https://www.kingdomplumbing.com', None, 'http://www.sincitypc.com', 'http://www.weprintwhatyouwant.com', None, 'https://ballantynecleaners.com/drop-store', None, None, 'http://www.fastfreshfoods.ca/', 'https://comfortcare.ca', 'http://www.calgary.ca/CSPS/Parks/Pages/Locations/SW-parks/North-Glenmore-Park.aspx', None, 'http://www.dontbebroke.com/?utm_source=Yelp&utm_medium=Location%2BPage&utm_campaign=Yelp', 'http://bobochinabuffet.com/', '1592182216', None, 'http://www.quiznos.com', 'http://www.bolocakery.com', 'http://benvenutos.com/locations/middleton', 'http://yourvalleyproperty.com', None, None, None, 'http://www.mehowey.com', 'https://www.alfredoshairsalon.com', None, 'http://www.flooptical.com/index.html', 'http://www.fineskincare.ca', 'http://www.iautocars.com', None, None, None, 'http://www.bk.com', '1592182267', 'https://www.walgreens.com/locator/walgreens-1801+philo+rd-urbana-il-61802/id=11368', None, 'http://www.closetworld.com', 'http://www.chicsincity.com', 'http://www.terribleherbst.com/', 'http://www.altardstate.com/', None, None, 'http://www.madisonpubliclibrary.org/monroe-street', None, 'http://www.corekitchenaz.com', None, 'https://stores.jcpenney.com/nv/henderson/clothing-stores-henderson-nv-2626.html', 'https://gymvmt.com', 'http://www.nynyhotelcasino.com/entertainment/bars/bar-at-times-square.aspx', 'http://www.symdonchevy.com/?cs:pro=repman&cs:e=yelp', 'http://www.dgapplianceandair.com', None, None, None, None, None, None, 'http://imageeyecarenv.com', 'http://www.mondaynightauction.com/', None, None, 'http://www.pool-spaoutlet.com', 'https://ameritekusa.net', 'http://www.nepps.net/contact-us', None, 'http://www.diamondcharlotte.com/', 'http://www.caferumba.net/', 'http://www.libertystationtavern.com', 'https://surrealnightlife.com/las-vegas/', None, None, 'http://7eleven.ca/store-locator/33259', 'http://www.thestretchdoc.com', None, 'http://www.drumandmonkey.ca/', None, 'http://www.thelivermorepgh.com', None, 'http://www.marriott.com/hotels/travel/pitel-springhill-suites-pittsburgh-bakery-square/', 'https://gelsbystormi.com', 'http://www.starbucks.com/store/9298/', 'http://www.magicwindow.ca', 'https://www.wellsfargo.com', None, 'https://www.marcosorder.com/?store=3582', None, 'http://yorktaps.ca', 'https://www.lasikmd.com/fr?utm_source=yelp&utm_medium=cpc&utm_campaign=calgary&utm_content=general-link&p_utc=YELP_paid', 'https://www.extraspace.com/storage/facilities/us/nevada/north_las_vegas/300030/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, None, 'http://www.fleetfeetcleveland.com', 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', None, None, 'https://local.lenscrafters.ca/on/thornhill/one-promenade-circle.html', None, "https://www.brueggers.com/?utm_source=yelp&utm_medium=homepage&utm_campaign=mayfield_heights&utm_term=Bruegger's%20Bagels%20Home%20Page", 'https://locations.wendys.com/united-states/al/madison/8814-hwy-20-w', None, 'https://www.bathdepot.ca/bath-depot-vaughan', 'http://www.lupitafernandezins.com?cmpid=d92d_blm_0006', 'http://www.aaatowing.ca', None, 'http://www.gilbertdentalcenter.com', 'http://fix8fitnesscafe.com/', 'http://www.jaroblue.com', 'http://fairwayindependentmc.com/', 'http://www.pittsburghwinery.com', 'https://www.wow1day.com/locations/house-painting-york?utm_campaign=yelp&utm_source=york&utm_medium=ubl', None, 'https://5starautocol.com', 'http://www.metrolinatire.com', None, None, 'http://palmerslawncare.net', None, None, None, 'http://www.tiffanymaidservice.com', 'http://www.reallysmooth.com', 'http://studio-kim.business.site', None, None, 'http://www.phohoa.com/', None, 'http://softmechanic.com', 'http://mastairaz.com', None, 'http://robertostacoshop.com', 'https://www.sonoraquest.com', 'http://www.dollar.com/Locations/gen.aspx?locationId=YTOC18', 'http://www.cpllabs.com/locations/patient-service-centers/cheyenne-psc.aspx', 'http://www.nguyenhuong.ca/menus.htm', 'http://www.fashionq1982.com', None, 'http://www.maddenbros.com', '1592182541', None, 'http://TresaApts.com', 'http://www.sanriva.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281379494&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://www.chevron.com', 'http://www.ruelo.com', 'http://burgerking.ca', None, None, 'https://www.uptowncleveland.com', None, 'http://www.dollartree.com/home.jsp', None, 'http://aerosportsparks.ca/brampton/', 'http://hummingbirddental.ca/', 'http://www.pghtours.com', '1592182590', 'http://www.amigotireslv.com', 'http://www.majesticmemorieslv.com/', 'http://www.eliteappliance.ca/', 'http://www.timhortons.com/', 'http://www.absolute-offroad.com', 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://www.deanshousestrongsville.com', 'http://www.sushiakaihana.com', None, None, 'http://www.sunocoinc.com', None, 'http://lvmpd.com/', 'http://lvdancesport.com', 'http://blasioleseatery.com', 'http://qualitycarstereoaz.com', 'http://www.sambucagrill.com', None, 'http://manhattandelimentor.com/', None, 'http://www.rockler.com/retail/stores/pa/pittsburgh-store', 'http://www.taxcomexicangrill.com', 'http://www.mobilespaelite.com/', 'https://www.walgreens.com/locator/walgreens-8500+w+cheyenne+ave-las+vegas-nv-89129/id=4197', 'http://www.bkreflex.com', 'http://Www.haringtonsplumbing.com', 'http://rjcrosby.com', None, 'http://www.coremotus.com/book-now', None, 'http://www.mathnasium.com/ocotillo', 'https://www.cleaneatz.com', None, 'http://www.gunsmithlasvegas.com', '1592182676', '1592182679', 'http://www.wachovia.com', 'http://www.secondcup.com', 'http://www.thelezzet.com', None, 'http://www.polishfestivalaz.org/', 'http://www.cmkpool.com', 'http://www.anniesgourmetitalian.info', None, 'http://www.cannabispatientcenter.com/', 'http://www.traderjoes.com', 'http://www.abcvalet.com', 'http://www.popshoppinautorepair.com', 'http://www.gnc.com', 'http://www.boldbeautyco.com', 'https://stores.thenorthface.com/WI/MADISON/USA24/', 'https://www.bannerhealth.com/locations/phoenix/banner-university-medical-center-internal-medicine', None, 'http://kimpovietnamese.com', 'http://familysbarbershop.com', 'http://www.olio.ca', None, 'http://www.dominos.com', 'http://onestopnutrition.com/', 'http://www.platinumcars.ca', 'http://www.fantasticfleamarket.com/', 'http://www.sapporopgh.com/', 'http://www.uniquedentalaz.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', None, None, 'http://www.theyogurtbaraz.com', 'http://www.papajohns.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/7499+West+Bethany+Home+Road+Corner+Of+75th-Glendale-AZ-85303/storeid=7872?cid=ps_ylp_2020', 'https://www.alohacleanersaz.com', 'https://www.mingsbubbletea.com', 'http://www.gokartslasvegas.com', 'https://www.brakemasters.com/location/5180-w-peoria-glendale-az/', '1592182778', None, 'http://www.cocochocolates.ca', 'http://www.showcaselandcare.com', None, 'http://www.bluewaveautospa.com', 'http://starfishandcoffeeshop.com', 'http://cohoots.com', None, 'http://shop.trisports.com/tempe', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282975370&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.nhmintviewobgyn.org/', None, 'http://www.stewartdetailing.com', None, 'http://bsalon11.com', 'http://www.northcoastlaser.com/', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', None, 'http://www.starbucks.com/store/9334/', 'http://kasianchiro.com', None, None, None, 'http://rtcsnv.com', None, 'http://monkeysushi.ca', '1592182939', 'https://www.bellagio.com/en/restaurants/sadelles.html', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', None, 'http://www.siegelsuites.com', 'http://www.bankofamerica.com', 'http://www.sloppykisseslv.com/', None, None, 'http://anthemhillsmusic.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.eliterepeatconsign.com/', 'https://www.zoup.com', 'http://thegymsportsbars.com', 'https://blackbeardiner.com/location/las-vegas-tropicana/', None, None, None, None, None, 'http://www.pachamamadc.com', 'http://www.econrads.com', '1592182988', None, 'https://www.jerseymikes.com/3128', 'http://www.indacutbarbershop.com/', 'http://www.pdubsbbq.com', 'http://www.bonaterrapgh.com', 'http://www.cessiespizza.com/', 'http://www.mark-taylor.com/arizona/ravenwood-heights/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.greatermatthewshabitat.org', None, 'http://www.modernchairrental.com', 'http://www.rhbarkleyhvac.com', None, None, 'http://www.riolasvegas.com/casinos/rio/restaurants-dining/hamadas-asiana-detail.html', 'http://accentricsalons.com', None, None, 'https://www.foodsocietyx.com', 'http://www.kay.com', 'https://www.eglintonsquare.ca', 'http://www.nicholascoffee.net', 'http://pinevilleplace.com', 'http://www.furry-pals.com', None, 'http://www.fantasticfades.ca', 'http://stratospherehotel.com/Food-Drink/Roxys-diner', 'http://www.villapizza.com', 'http://phoenixshoulderandknee.com/', '1592183053', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.sjnc.org/', '1592183060', None, 'http://fixautousa.com/las-vegas-north', None, 'http://www.lasvegas-cars.com', 'http://www.brimhallwellnesscenter.com', 'http://www.english.fgs2.ca/', None, None, 'https://locations.churchs.com/nc-charlotte-598', 'http://www.europeanautosalon.com', 'https://www.interdent.com/gentle-dental/locations/az/peoria/14155-n-83rd-ave-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.secondheartyoga.com', None, 'https://www.infinitiofbrampton.com', None, 'https://www.jlrichardscatering.com', 'https://madison.madhouseexperience.com', 'http://www.tempeuniversityinn.com', None, 'http://www.andersonaudiology.com', 'http://www.fionnmaccools.com', None, 'http://www.gelogisticsolutions.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.hairclub.com/locations/on/mississauga/hair-loss-clinic-228/?pub=loclisting&utm_source=yext&utm_medium=loclisting&utm_campaign=YX_228', 'http://www.hotyogatnt.com', 'https://locations.theupsstore.com/pa/mcmurray/4017-washington-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.cinemark.com/theatre-detail.aspx?node_id=97350', 'http://www.cuyahogalibrary.org/Branches/South-Euclid-Lyndhurst.aspx', 'http://www.wepoundemfishing.com', 'http://www.serviceking.com/locations/service-king-puritas?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://www.alsautorepair.mechanicnet.com', 'http://novabellasalon.mysalononline.com', 'http://www.cleatsinc.com/', 'https://phoenix.legacytraditional.org', 'https://beautyboxbyella.business.site', 'http://costcutters.com/salondetail/default.asp?salonid=62180', 'https://www.lafolieresto.ca', None, 'http://www.costco.com/WarehouseLocatorDetailsView?warehouseNumber=1121&storeId=10301&catalogId=10701', 'http://lakesidegrillestrella.com', 'http://www.barrecleveland.com/', 'http://www.cafemoka.us', 'http://www.midas.com/lasvegas/store.aspx?shopnum=1192&dmanum=480', 'http://www.verizonwireless.com/stores/arizona/tempe/tempe-marketplace-1088402/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://junskoreanlv.com/', 'http://www.smoothieking.com', 'http://restorecoldpressed.com', None, 'https://www.choicehotels.com/CN280?mc=blypypaf', 'http://www.earlyeducationpros.org', 'https://www.milansalonaz.com', 'http://www.tappsbar.com/', None, 'http://www.makisushi.ca', 'http://vibrantcare.com', None, 'http://www.marshallscanada.ca/en/directions.aspx?sid=741', 'http://www.thornhillskinclinic.com', 'http://www.union.lib.nc.us', '1592183182', 'http://buysellrent702.com', None, 'http://www.sugarshackaz.com', 'http://www.pizzahotwings.com', 'https://www.pizza73.com', 'http://allpages.com/', 'http://hairtiquedesignersinc.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.hunkmansion.com', 'http://www.nellos-pizza.com/', None, None, 'http://www.andrewleohairsalon.com', None, 'http://www.fullhousedesserts.ca', 'https://www.symphonywed.com', 'http://www.homesteadkennels.com', None, None, 'https://www.lasvegaseliteoffroad.com', None, None, None, 'http://www.dogworksmpg.com', 'http://www.rosarium.ca', 'http://www.piecesunimagined.com/', None, 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', None, 'http://www.groundsguys.com/madison', 'http://www.lovetowax.com', 'https://nailuxx-nail-salon.business.site', 'http://www.mooreinjurylaw.com', 'http://myfriendsrestaurant.com/site/', None, 'https://www.tillys.com/store?StoreID=0045', 'https://www.mosquito-authority.com/locations/scottsdale-az/', 'http://www.thesteammasters.com', 'https://www.thetreesurgeonpa.com', 'http://www.albertsgifts.com', None, None, 'https://www.usps.com/', 'http://www.kingorthodontics.com', None, None, 'http://tailsandscales.ca/', '1592183275', None, 'http://www.papajohns.com/', 'http://www.buonafurniture.ca', 'https://local.biglots.com/ky/henderson/190?zcp=pd_local_yelp', 'http://www.freshlysqueezed.ca', None, 'https://stores.nordstromrack.com/us/oh/westlake/30121-detroit-rd?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=277&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', None, 'https://celebritytheatre.com', None, 'http://www.ryanhomes.com', 'http://www.bwmpetresort.com', 'http://www.diblasisbakery.com', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281380850&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.goldenspoon.com/', 'http://www.starrtreatments.com/', 'https://greatchoicechiro.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://cardenaslawgrouplv.com', 'http://www.coldstonecreamery.com/stores/20008', None, 'http://www.circlek.com/', 'http://www.vegasdiscountnutrition.net', 'https://islandpacificmarket.com/stores/listing/tropicana', 'http://www.madisonwindowtint.com', 'http://www.brueggers.com', None, 'http://giu.ca', None, None, 'http://www.paintingcontractorsohio.com', None, 'http://www.hmsmokeshop.com', 'http://www.sunsetboatrv.com', 'http://www.welderup.com', None, 'http://www.revolution-games.com', 'http://www.rocksidefamilydentalcare.com', 'http://www.accphx.com', 'https://locations.monro.com/pa/sewickley/209-ohio-river-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.lumosarts.com', None, 'http://www.saswax.com', 'http://www.crutcherauto.net', 'http://www.puttersvegas.com', 'https://palmbeachtan.com/locations/AZ/Peoria-West-Thunderbird-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'http://clevelandhenna.com', None, None, 'http://www.sageandsandgrill.com', 'http://www.fillsgas.com', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', None, None, 'http://www.tonycordellphotography.com', '1592183388', None, 'http://www.cornerbarrestudio.com', None, 'http://www.bk.com', 'http://www.balletbarreworks.com', 'https://www.ghcscw.com/clinic/Hatchery%20Hill%20Clinic', 'https://www.la-z-boy.com', 'http://www.ecig-emporium.com', 'http://abcpoolservice.net', 'https://etobrestaurant.business.site', 'http://www.otherwideshoes.com', 'https://catchersfish.com', 'http://www.tigerkimstkd.com', 'https://www.take5oilchange.com/locations/oh/euclid-125/', None, 'http://www.esspa.net', 'http://www.allsewingmachinerepairs.com', 'https://www.sunrisepreschools.com/locations/broadway-mcclintock/?utm_source=yelp&utm_campaign=online_listing_tempe_274&utm_medium=referral&utm_term=business_url', None, 'http://planetzong.com/', 'https://www.choicehotels.com/pennsylvania/pittsburgh/comfort-inn-hotels/pa354/rates', 'http://www.starbucks.com/store/8054/', 'http://www.pillarcrowncourt.com', None, 'http://www.greenvalleyranchresort.com/dining/sushi-sake.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=GVR&utm_content=GVR-PROPERTIES&utm_campaign=GVR-YELP', 'http://CallAdvancedPro.com', 'https://www.bagelnash.ca', 'https://www.homedepot.com/l/Arrowhead-Ranch/AZ/Glendale/85308/475?cm_mmc=seo-yelp&', None, 'http://www.mattressfirm.com/', None, None, 'http://www.thepowerplant.org', '1592183453', 'http://www.donsbusbox.com', 'http://cheshirecataz.com/', 'http://www.dentistinstow.com', 'http://www.antiquecenterofstrabane.com', 'http://www.pointmanagementgroupllc.com', 'http://brightonevents.ca', 'http://www.autorepairaz.com', 'http://www.timelesshealthclinic.com', None, 'https://www.flyswoop.com', 'http://southpointcasino.com/dining/michaels-gourmet-room?cid=ypmic', None, None, None, None, 'http://www.bedfordnissan.com/', '1592183486', None, 'http://www.planetbouncepgh.com', None, None, None, 'http://www.jrlighting.com', 'http://monsoongroup.ca', '1592183503', 'http://www.familydollar.com', 'http://www.sachisalon.com', None, 'https://www.stancatos.com', 'http://www.substationii.com', None, 'http://www.ccdgp.com/', 'http://uhaul.com', 'http://wienerschnitzel.com/', 'https://www.wherefamiliesgrow.com', 'http://www.corksplayhousesquare.com', 'http://www.tempedogs.com', None, 'http://www.blowit.ca', None, 'http://www.thewokker.com', None, 'http://www.gianteagle.com', 'http://www.calgarybikram.com', 'http://www.fortresscreditpro.com/', 'http://www.honeymee.com', 'http://schnitzel.ca/', 'http://www.freshens.com', None, None, 'http://www.squashblossomaz.com', 'http://www.saharacenterlv.com/', None, 'http://www.unitedmayflower.com?Cpgn=Yelp', None, None, None, 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'http://ahwatukeehoa.com', None, 'https://www.scenariopgh.com', 'https://www.carowinds.com/things-to-do/dining', None, None, 'https://www.petsmart.com/stores/us/az/glendale-store0157.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://fastfix.com', 'http://www.starbucks.com/store/11823/', 'http://www.shapirocho.com', 'https://www.hungryhowies.com/store/hungry-howies-01824?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=1824&utm_content=Website_Link', None, 'http://www.metromoversgtanorth.ca', None, 'https://westernhonda.com', None, 'http://www.quiktrip.com', 'http://www.jeffspeakmanlv.com', 'http://www.fmentertainment.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=891&utm_content=bpas', 'https://www.gggflorist.net', None, None, None, 'http://www.birtsbistro.com', 'https://www.thepercantileandcreamery.com', 'http://www.geniusnetworkevents.com', 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=531', 'https://www.pinnaclemoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.glazecraze.ca', None, 'http://adfarm.mediaplex.com/ad/ck/24347-208272-18214-3', 'http://charlotteplumbing.com', 'https://stores.loft.com/outlet/us/nv/las-vegas/7400-las-vegas-blvd-south.html', 'https://www.wellsfargo.com', None, 'http://www.guess.com', '1592183651', 'http://www.therosehairstudio.com', 'http://www.cookmortgagegroup.com', None, 'http://www.LasVegasSegway.com', 'http://bennettautocare.mynapatools.com', None, None, None, 'http://www.kfc.ca/store/27-ruth-ave-brampton', None, 'http://www.lcbo.com', 'http://88noodlepapalasvegas.cafescentral.xyz', 'http://www.endurancerehab.com', 'http://www.rennsportire.ca', 'http://ladydianascakes.com/', 'https://locations.wendys.com/united-states/oh/cleveland/13939-euclid-ave.', None, 'http://www.MDA-Dentist.com/', 'https://ad.doubleclick.net/ddm/clk/300113982;127047679;f', None, 'http://www.toucheh.com', 'http://www.deathsdoorspirits.com', 'https://www.appliancepartscompany.com', 'http://www.toronto.ca/parks/island/', 'https://www.cinemark.com/arizona/cinemark-mesa-16', 'http://www.madisoninternationalspeedway.com', 'http://www.koolkatpgh.com', 'http://www.appliancesrepaircalgary.ca', None, None, None, 'http://www.reno4men.com/', None, 'http://scottsdale.house.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_phxxs_en_homepage_desktop&code=YB', 'http://www.servicecanada.gc.ca/tbsc-fsco/sc-dsp.jsp?lang=eng&rc=4802', 'http://ginassalonandwigs.com', None, 'http://phxnightclub.com/', '1592183735', None, 'http://www.heersmanagement.com/properties/property/del-mar-terrace-apartments', 'https://www.minutesuites.com', 'http://www.urban-baker.ca/', 'http://www.cactuslv.com', 'http://www.kandagreenhouse.com', 'http://englishhedgerow.com', 'http://www.universalcupcoffee.com', 'https://www.carmax.com/stores/7197?adcode=YLP7197&utm_campaign=LG_AFF&utm_source=LG_AFF_YLP&utm_medium=local&utm_content=shop', None, 'https://locations.dignityhealth.org/st-joseph-s-westgate-medical-center-glendale-az', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1015+East+Ray+Road-Chandler-AZ-85225/storeid=7849?cid=ps_ylp_2020', None, None, 'http://yotapros.com/', 'https://www.giantmanhattanpizzaphoenix.com', None, None, 'http://www.masalakitchen.ca', 'http://www.zachmonroytraining.com/', None, 'http://www.livinggrace.net', 'http://homewoodsuites3.hilton.com/en/hotels/ontario/homewood-suites-by-hilton-toronto-markham-YYZHWHW/index.html?SEO_id=YELP-HW-YYZHWHW', 'https://stores.columbia.com/chandler-factory-store', 'http://www.wegotgamez1.ca', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, None, '1592183793', 'http://www.murphyappliance.ca', 'http://www.silkroadsushiandsteakhouse.com', 'http://www.mycdi.com/arizona/locations__services/', None, 'http://www.mypeacepreschool.com', 'https://www.inschoolwear.com', 'http://www.silverminesubs.com/', 'http://www.Arizonarvservice.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.saharavegas.com/food/HouseofLords/', 'http://www.applianceservicecentre.ca', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.lesolson.com', 'http://www.phoenixpublicmarket.com/', None, None, None, None, 'http://www.theprophysiques.com/#home-top', 'http://www.eta-az.com', 'https://www.pizza73.com', None, None, 'http://radiocitypizza.com', 'http://www.yaharabay.com', None, None, 'http://www.ontariocourts.on.ca/scj/en', None, 'http://www.primroseestates.com', None, 'http://www.zonacaffe.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.jcsgrillhouse.ca/markham/', 'http://www.womensspecialtycare.com', None, 'http://www.ipetgrooming.com', None, 'http://www.perkykettle.com', None, 'http://www.tazzyandboo.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://alorestaurant.com/', None, 'http://Vegasonlinerealty.com', None, 'http://www.cynthiaschinese.com', 'https://locations.traderjoes.com/az/gilbert/258/', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.bestfloorcoatingsaz.com', 'http://www.scottsdalememorycare.com', 'http://www.evans-properties.com', 'http://www.lidlounge.com', 'https://www.supercuts.com/locations/az/surprise/albertsons-shopping-center-haircuts-82334.html', 'http://www.apnihavelly.com/', 'http://www.swisschalet.com', None, None, 'http://www.yangteashop.com', '1592183914', None, 'https://www.originaljoes.ca', None, None, 'http://www.BASISgoodyear.org', 'https://www.goodyear.com/en-US/tire-shop/Phoenix+AZ+85016-6808+US/000121764', 'https://www.pizzahut.ca/store-details/store-R42601/pizza-hut-Stouffville', None, 'http://www.foodlion.com', 'http://www.kegsteakhouse.com/en/locations/ON/toronto/esplanade-keg/', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.patelbros.com', None, 'http://blomedry.com/locations/blo-strongsville-ohio/', 'http://stylehousebeautybar.com', 'http://calgarysbestpubs.com/joyce/', None, 'http://www.artbuscoffee.com', None, 'http://www.galleriasm.com/branch/store/th', 'http://www.morcandirect.com', None, 'http://daluhairdressing.com', None, 'http://www.theencorequartet.com', 'http://www.unclebenspawnshop.com', 'https://www.olivegarden.com/locations/az/phoenix/metro-center/4410?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:phoenix-az-4410_pl:locurl_rd:1754', 'https://www.daveandbusters.com/locations/canada-oakville', 'https://www.westerndental.com/en-us/find-a-location/arizona/phoenix/13651-n-35th-ave', None, 'http://cargilleyecare.com', 'https://www.charmecochinchine.com', 'http://locations.michaels.com/nc/charlotte/5032/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://womensbookstore.com/', None, None, 'http://www.stellamiawestlake.com', 'http://cahairsalons.com', None, 'http://www.svahayogacenter.com', None, 'https://www.choicehotels.com/north-carolina/pineville/quality-inn-hotels/nc384/rates', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.theartofvapes.com', 'https://www.jetspizza.com/stores/illinois/champaign/512-s-neil-st?utm_source=Yelp-Ads&utm_medium=Yelp-Ads-SEO&utm_campaign=IL-008&utm_content=Website', 'http://www.cactuscrossfit.com', 'http://www.safeway.ca', 'http://justdogsgourmet.com', None, 'http://www.studio480thesalon.com/', None, 'https://southcharlotteservices.org', None, 'http://btnfurniturerepair.com/', 'http://www.bojangles.com', 'http://www.mississauga.ca/portal/discover/braebengolfcourse', 'http://exclusivecustomslasvegas.com', 'http://www.somersfurniture.com', 'https://no900.com', None, None, None, None, None, 'https://www.stateandmain.ca', 'https://www.ttc.ca/Subway/Stations/Pape/station.jsp', 'http://www.washwag.com', 'http://www.ritasfranchises.com/ArcadiaTowneCenter', 'http://www.loova.com', 'http://www.xpandrealty.com', '1592184055', 'http://www.petagreemobilespa.com/', 'https://www.simplyravishingsalon.com', 'http://www.dreamtherapies.com/', None, 'http://www.perrinofurniture.com', 'https://www.guaranteedrate.com/loan-expert/joecordone', 'http://www.strudelteig.com', '1592184073', 'http://www.bremec.com/BremecOnTheHeights.htm', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.arizonaroofingcompany.com/', None, 'http://www.anthropologie.com/', '1592184083', 'http://www.firstcu.coop', 'http://www.gristle.catering', 'http://www.hartswastedspace.com', 'https://www.chilis.com', 'http://www.elementalplumbing.com', 'http://www.northmountaingrille.com', None, 'http://www.meridiancu.ca', 'http://www.elitemoversofcleveland.com', 'http://www.jackalopejacks.com/', None, 'http://www.avenueliving.ca', None, 'https://www.hudsonsrestaurant.com', 'http://www.yojuicylife.com', 'http://bloorwestcosmetics.ca/', None, 'https://locations.nekterjuicebar.com/ll/US/AZ/Phoenix/4340-Indian-School-Rd_*-Ste_-19?utm_source=yelp&utm_medium=link&utm_campaign=Indian-School&utm_content=URL', 'http://www.vintagethai.ca', None, '1592184122', 'http://www.artistsuncorkd.com', None, 'http://www.tiedemannglobe.com', 'http://saveamuttkennel.info', None, 'http://www.bedsidemanor.com/', 'http://www.silversevenscasino.com/', None, 'http://www.lobbyrestaurant.com/', None, 'http://lindeyslakehouse.com', None, 'https://www.ubreakifix.com/ca/locations/thornhill', 'http://kwikkleaning.webs.com/', 'http://www.gemoftheearth.com', 'http://www.charlottelaserdentist.com', None, None, None, 'http://www.exquisitenailsandspa.ca/', None, 'http://www.jfcsaz.org/site/c.ajIQK6NMLfJ0E/b.6211177/k.2AE8/Contact_Us.htm', 'https://tabletennisandmore.com/phx/tabletennisandmore/', None, 'http://www.7-eleven.com/?yelp=22886', None, None, 'http://www.bodytherapyaz.com', None, 'http://www.westvalleypetsitting.com', None, 'http://www.capitano.ca', 'http://www.renusskincare.com', 'http://scorpionridge.com', 'http://www.cfcgiftcard.com', 'http://www.sandovalkarate.net', 'https://abrazomedicalgroup.com/amg-parkway/robert-l-bierman-md/', 'http://www.lifeisbeautifulsalon.com', 'http://www.upnsmokepitbbq.com', 'http://www.kensingtonmakeup.com', 'http://www.saryocafe.com', None, 'https://www.interdent.com/gentle-dental/locations/az/phoenix/4910-e-chandler-blvd-dentist-office?utm_source=organic&utm_medium=yext', None, 'http://www.reposesalonandspa.net', None, None, 'http://www.xingfutang.ca', None, None, 'http://www.challengerbasic.com', 'http://www.farrarjewelers.com/', 'http://www.oakandvine.ca', None, None, 'http://northernhillsdental.com', 'http://www.madvapesindianland.com', 'http://4sonsstores.com/29', None, 'http://www.cashamerica.com/SUPERPAWN-stores/NV/LASVEGAS/LV02', 'https://www.ubreakifix.com/ca/locations/avenueroad', None, 'https://www.hamiddonair.com', 'https://only-inspections.com', 'http://www.restauranttrentina.com/', None, 'https://www.petsuppliesplus.com/Store/SC/Fort-Mill/Fort-Mill/4189', None, 'http://www.skinnywimpmoving.com', 'http://www.auntieannes.com', None, 'http://www.toshoknifearts.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216608&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://wisconsinrepair.com', None, 'http://www.valleysolaraz.com', 'https://www.walgreens.com/locator/walgreens-1159+e+southern+ave-mesa-az-85204/id=3670', 'https://www.cineplex.com/Theatre/cineplex-cinemas-winston-churchill', 'http://www.peaksathleticclub.com', 'https://www.servproscottsdale.com', 'https://www.ventitobakery.com', 'http://www.northscottsdalehyundai.com/', None, 'http://www.metrofireaz.com', None, 'http://www.wingstop.com/', 'http://www.sallybeauty.com', None, None, 'http://hrhc.lv/PinkTaco', 'http://www.addisononerinmills.com/', None, 'https://local.fedex.com/nv/las-vegas/office-1441/', 'http://www.heartpathacupuncturemadison.com/', '1592184312', 'http://www.carolinaexpressclinic.com/', 'http://www.insuranceinwhiteoak.com?cmpid=ts6n_blm_0006', 'http://www.apachewellscountryclub.com', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/mississauga-2191-dundas-street-e.aspx', None, 'http://www.bathandbodyworks.com', None, 'http://www.bestbuy.com', 'https://iisnv.com', 'https://www.topmasterlocksmith.com', 'http://www.lowes.ca', 'http://www.primrosehuntersville.com?utm_source=yelp&utm_medium=maplistings&utm_campaign=localmaps', 'https://stores.jcpenney.com/wi/madison/clothing-stores-madison-wi-0891.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-0891', 'http://www.mcdonalds.com', 'https://1stpetvet.com/locations/north-valley-az/', None, 'http://www.rxboilerroom.com', None, 'http://www.brakemasters.com', 'http://www.familydollar.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://liasgardenbanquethall.com', 'https://www.menswearhouse.com/store-locator/2505?utm_source=yelp&utm_medium=listing&utm_content=2505&utm_campaign=AZ', 'http://freshmexican.wix.com/hermanos', 'http://www.miramaestudio.com/#!services/c166e', None, None, 'http://www.harrisgrill.com', 'http://www.tiffany.ca/', 'http://www.saloonofmtlebanon.com', 'http://priorityonefit.com', None, 'http://www.miseryinktattoobodypiercing.com/', 'http://hongto.weebly.com/', 'https://solsouthwestkitchen.com/#locations', 'http://nexusrehabspine.com/phone/index.html', 'http://www.vivaladivalv.com', 'http://www.eastcoastweapons.com/', 'http://www.arizonaglasspros.com', None, 'https://www.fishertools.com', None, 'http://panzapiena.ca', None, 'http://www.sunocoinc.com', 'http://redwagondiner.com/', None, 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', '1592184420', None, 'http://local.firestonecompleteautocare.com/arizona/peoria/10661-n-84th-ave/?lw_cmp=IYP_YPC_MLP_11932', 'http://www.starbucks.com', 'http://www.thenailroomlv.com', 'http://www.nunziospizzeria.com', None, 'https://shopmarketandco.com/merchant/seed-to-sausage/', 'http://www.clarkcountynv.gov/Depts/parks/Services/pages/picnic-area-reservations.aspx', 'http://www.azstudentmovers.com', 'https://www.itcu.org/about/locations/green-valley', 'http://www.runningroom.com/hm/inside.php?id=2332', None, 'http://www.pareagyros.com', 'http://paladinautomotivelasvegas.com', 'http://automaticgaragedoorcompany.com', 'http://www.azcentral.com', 'http://www.gotourscanada.com', 'http://commercialcenterdistrict.com', 'https://thesaguaro.com/scottsdale/#hotel-spa', 'http://www.einsteinbros.com', 'https://www.desertstateinspections.com', 'http://local.firestonecompleteautocare.com/north-carolina/charlotte/5340-e-independence-blvd/?lw_cmp=IYP_YPC_MLP_10790', 'http://www.clarkcountynv.gov/Depts/parks/Pages/clark-county-museum.aspx', 'http://www.goodlifefitness.com', 'http://www.eSMIL.com', None, 'https://moxies.com/restaurant-locations/ontario/richmond-hill-beaver-creek', 'https://twomaidsgilbert.com', None, 'https://my.clevelandclinic.org/locations_directions/regional-locations/avon-lake-fhc', None, None, 'https://www.redlobster.ca/locations/list/on/toronto/20-dundas-street-west', 'http://www.dvfmaz.net', None, 'http://thevaporloft.com/', 'http://www.dineoncampus.com/UNCCharlotte/', 'http://www.celebrationsbarandgrill.com', 'http://heyrestaurant.tumblr.com/', 'http://www.dunkindonuts.com', None, None, None, None, 'http://www.clarkcountynv.gov/depts/parks/Pages/parkslocator.aspx', 'http://www.dillonsontopofcentral.com/', 'http://www.omegahomeimprovements.com', 'http://talleyproperties.com', None, 'http://www.chandelier-hair.com', 'http://www.serenityflorals.com', 'http://hbsalonnc.com', 'https://www.crawfordsautoservice.com', 'http://www.newsons.ca', 'https://www.tempevistabyavanti.com', None, 'http://www.leons.ca/', 'https://www.giuseppeson28th.com', 'https://diamondlaw.ca/toronto', None, None, 'https://www.greulichs.com', None, None, 'http://www.scottsdaleskininstitute.com/', 'https://germancarspecialist.com', 'https://locations.wendys.com/united-states/pa/swissvale/1703-s.-braddock-ave', 'http://www.greekvillagegrille.com/', 'http://www.neptunehairstyling.com', 'http://www.dollartree.com', None, 'http://www.trucksonlysales.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Calgary-AB-T2Z4M8/058072/', 'http://www.karenshairdesigns.com/', 'http://mothernaturesdiapers.com/', 'http://www.arizdental.com', 'http://www.johnnysonfulton.com', 'https://agents.allstate.com/adam-brown-las-vegas-nv-14515251.html', 'http://www.lasvegasdiscountbeds.com', 'http://www.cactuspools.com/', 'http://www.skytecsecurity.com/', 'http://paintingcontractorglendale.com', 'http://www.carters.com/home?id=carters&cm_mmc=Retail-_-Carters-_-Yelp-_-April', None, 'http://azempiredoors.com', 'https://www.millers.com', None, 'https://thegoatbarandgrill.com', None, 'https://davids-diner.business.site', 'http://www.clevelandart.org', None, 'http://theclevelandarcade.com/', 'https://locations.jackinthebox.com/us/az/chandler/900-n-cooper-rd', 'http://www.gap.com', 'http://www.janetscustomsewing.com', '1592184613', 'http://xtremecleanmobile.com', 'http://sfsourdougheatery.com/', 'http://www.randitas.com', 'http://steliotesdentalspa.com/', None, 'http://www.sushisushi.ca/', None, 'http://www.duzz.ca', None, None, 'https://arizona.weidner.com/apartments/az/phoenix/skyline-lofts-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'https://dealer.sprint.com/experts-choice', 'http://www.aztecatowingarizona.com', 'http://mannysdiscount.com', None, None, 'http://www.sterlingsteelecreek.com', 'https://www.nofrills.ca/store-locator/Dennis%27+nofrills+%28Erin+Mills+Parkway%29/0700?storeId=0700', 'http://www.libertyfordbrunswick.com/', 'http://pro-techtransmission.com', 'http://www.cozumelrestaurante.com', 'https://www.choicehotels.com/pennsylvania/pittsburgh/quality-inn-hotels/pa476?source=pmfyelp&pmf=yelp', 'http://www.scottmillerdds.com/', 'https://www.escapecampervans.com/locations/las-vegas-nevada/', 'http://automotiverepairphoenix.com', None, 'http://www.bathandbodyworks.com', None, None, None, 'http://www.a1qualitycare.com/', 'http://madisongaragedoorservices.com', 'http://local.firestonecompleteautocare.com/arizona/mesa/1553-s-crismon-rd/?lw_cmp=IYP_YPC_MLP_784290', 'http://petstellthetruth.com/', 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'https://www.dentistryatgreenway.com', 'http://duckyschampaign.com', 'http://www.paddyspourhouse.com', None, 'http://www.saffrontakeout.ca', 'http://www.overflowcafe.com', 'https://www.bankofamerica.com', 'http://msquarecoffeeco.com/', 'http://Clearqualityautoglass.com', 'http://www.nicolebodyworks.com', 'https://www.homedepot.com/l/Avon-Vail/CO/Avon/81620/1525?cm_mmc=seo-yelp&', '1592184707', None, None, 'http://99only.com/store/Phoenix---12th-St./', 'http://www.oasispediatrics.com', 'http://www.krispykreme.com', 'http://www.calgaryscrapautoremoval.com', None, None, None, 'https://jamesgoodnow.com', 'http://www.nps.gov/lake/index.htm', 'http://www.aiellospizzeriallc.com', None, 'https://local.fedex.com/az/glendale/office-1471/', 'http://pecoslawgroup.com', 'https://www.handlebarj.com', 'http://www.courtoneaz.com/', 'http://www.desertrad.com', 'http://trubliss.com', 'http://hotduckaz.com', 'http://www.starbucks.com/store/14887/', 'https://glassdoctor.com/henderson', 'http://www.momdocwfw.com/scottsdale', 'https://www.calforex.com/en/locations/foreign-exchange-vaughan-on-vaughan-mills/', 'http://www.truwest.org', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.designateddriversinc.com', None, 'https://f45training.com/southwestlasvegas/home', None, None, 'http://bellavitaitaliangrille.com/', None, 'http://www.mark-taylor.com/arizona/san-lagos/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.azhomedefense.com', '1592184786', None, 'http://www.hooters.com', 'http://www.atlccleaningcompanyllc.com', 'http://christinanailboutique.com', None, None, 'http://tamidairiki.md.com/', 'http://www.azallergy.com', 'http://www.DymeBoxing.com', None, 'http://www.toplimolasvegas.com', 'http://livingwellhomes.com/apartments/details/brookfield_homes', 'http://www.dermsolutionsaz.com/', 'https://wickenburg-alternative-medicine.business.site', 'http://www.lapetite.com/your-local-school/north-las-vegas-nv-7306', 'http://lasvegasstripweddings.com/', None, None, 'http://www.newamericanagent.com/steveschauer', 'http://www.ocean-prime.com/locations-menus/phoenix', None, 'http://tajindiancuisineaz.com', 'http://www.adidas.com/us/storefinder', None, '1592184835', 'http://ranchosecurity.com/', None, 'http://www.foodlion.com', 'http://www.thebeadery.ca', 'http://www.othermothersaz.com', None, 'http://www.esmokercanada.com', None, 'http://www.carmodysgrille.com', None, 'http://littlemacau.com/', 'http://AnimalCareClinicInc.com', None, None, None, 'https://www.hilton.com/en/hotels/phxruru-tru-gilbert/?SEO_id=YELP-RU-PHXRURU', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.tocasierraspa.com', 'http://www.buffalowildwings.com/?utm_source=yelp&utm_medium=yelp_profile&utm_campaign=yelp_locations', None, 'http://www.fortmcdowellcasino.com/home.php', 'http://www.pridebeautystudio.com', 'http://www.restaurantrouby.ca', 'http://sawasdeethaitogokitchen.com', 'https://mountainsidefitness.com/locations/carefree/', 'http://www.copps.com/', 'http://locations.saksoff5th.com/en/phoenix', 'http://www.canadiantire.ca/en/store-locator/ab/calgary-south-ab.store.html', 'http://www.hansonwater.com', 'http://www.gussdiner.com/', None, 'http://ladoniacafe.com/', '1592184905', None, None, 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/toronto-center-(1).aspx', 'https://www.floristinrockyriveroh.com/?srccode=yelp_track', 'http://www.menasgrill.com', 'https://gohoneyhut.com', 'https://footsolutions.com/phoenix/', None, None, None, 'http://www.minervaindiancuisine.com/', 'http://savoypgh.com/', None, 'http://www.peoples-gas.com', 'http://www.shopjustice.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'http://www.bollywood-bites.com', None, 'http://myazlawyers.com/', 'http://heartschoices.com/calgary-farmers-market/', None, 'http://www.dicey.biz', 'http://crazyburrito.ca', 'http://www.Montblanc.com', '1592184965', 'http://www.beadworldinc.com', 'http://www.lvcharleston.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, None, None, None, None, 'http://www.muchoburrito.com', 'http://www.pitaland.ca', None, None, None, 'http://www.rideabike.com', 'http://www.shicklaw.com', 'http://www.revivestainlesssteel.com', 'http://www.thebespokeman.com', 'http://www.cavecreeklock.com', 'http://www.chestermerelanding.com', 'https://www.canyonstateauto.com', 'http://6ixbar.com', 'https://www.regmovies.com/theaters/ua-showcase-theatre-8/C00542780062', None, None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7784&localechange=1', 'https://www.aldoshoes.com/us/en_US/store-locator/store/2103', 'http://www.kingsrestaurant.net', None, None, None, 'http://www.sarahhorne.org', None, 'https://www.rentvegas.org', 'https://cocktailantabli.com', 'http://dosgringosaz.com', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', None, None, None, 'https://www.fsequence.photography', 'http://www.petgroominglv.com', None, 'http://www.mississauga.ca/portal/residents/mississaugavalleylibrary', None, 'https://oakarizona.com', 'https://www.nightowlcontractors.com', None, 'http://robertostacoshop.com', 'http://gravady.com', 'http://www.humblepieusa.com/', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=14057&localechange=1', None, 'http://www.farwellpools.com', 'http://www.bin110.com', 'http://www.crocs.com', 'http://tricitycardiology.com', 'http://www.larkspurcatclinic.com/', 'https://www.sunrisechildrenshospital.com', None, 'http://www.theroofdoctorlv.com', None, 'http://www.altacamelback.com', 'https://locations.timhortons.com/ca/on/oakville/494-dundas-st-w.html', 'https://www.currys.com', 'http://perfecthomefurniture.com', None, 'https://www.abraauto.com/abra-auto-location/1058-concord-nc', 'http://www.patricksimonedds.com', 'http://www.lvendocrinology.com', 'http://www.chandlerapthomes.com', 'http://www.desirableskinaz.com', 'http://www.flooringsurfacesinc.com', 'http://www.travelgolfcenter.com', None, 'https://www.jetblue.com', 'https://www.bahamabreeze.com/locations/nv/las-vegas/las-vegas/3020?cmpid=br:bb_ag:ie_ch:dry_ca:BBQ121LOCURL_dt:20200605_sn:yelp_gt:las-vegas-nv-3020_pl:locurl_rd:1013', 'http://www.weknowurban.com/Phoenix/', 'http://www.thorncliffebowlerama.com/', 'http://www.queenspectacle.com/', 'http://www.linenchest.com', 'https://www.redrobin.com', None, None, '1592185140', 'http://lemontblancbanquets.ca', 'http://nolimitska.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.highlandfarms.ca', 'http://www.firkinpubs.com/thefrogandfirkin/', None, 'http://www.papamurphys.com/', None, None, 'http://www.dacordplumbing.com', 'https://www.championwindow.com/Cleveland/?lpc=UU-OD-Cleveland-Yelp&source=ol-yel01&utm_source=yelp&utm_medium=local&utm_campaign=Cleveland', 'http://bundtz.com', 'https://caringhandsvetlv.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://clearchoicetechnical.com/service-locations/las-vegas', 'http://www.devinetouchmassage.com', 'http://www.nirvanahome.ca/', 'http://www.robertgodridgephotography.com/', 'https://www.maidsinblue.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.enblumcatering.com', 'https://atriumhealth.org/locations/detail/carolinas-medical-center-mercy', 'http://www.gilbertazpediatricdentist.com/', 'http://www.screwielewies.com/', '1592185190', 'http://www.sapporolv.com', 'http://www.galaxyhobby.ca/', 'https://azpyramidservices.binbooker.com', None, None, None, 'https://www.modernround.com/locations-peoria.html', 'http://livingwelltakeout.net/', 'http://www.balletossington.com/', None, '1592185212', 'https://agents.farmers.com/az/chandler/joe-baselice?SourceID=AMPALFYEAG&utm_medium=Local&utm_source=Yelp', None, 'https://www.get-go.com', 'https://www.ulta.com/stores/glendale-wi-646', 'https://www.cox.com/local/residential/stores/az/gilbert/2150-east-williams-field-rd?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q36', 'https://www.olivegarden.com/locations/az/phoenix/metro-center/4410?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:phoenix-az-4410_pl:locurl_rd:1754', None, 'http://www.passionfordesserts.ca', 'https://www.aqua-tots.com/chandler/', 'https://www.handy.com/yelp50cc?utm_source=yelp&utm_medium=CPC&utm_campaign=TOR-Handy-Yelp', 'http://www.xcash.ca', None, 'http://www.mysweetbasil.com', 'https://www.sassoon-academy.com/en/academy/north-america/toronto', None, None, 'http://www.toytownplaycenter.com', 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/twinsburg-fhsc', None, 'http://www.tabbyandjacks.com', None, None, 'http://enhancedcare.ca', None, 'https://www.gianteagle.com/Stores/Store/?storeId=224', None, 'http://www.kay.com', None, 'http://www.jimshorkeyford.com/?ibp-adgroup=YX_Target', None, None, None, 'https://www.granitetransformations.com/location/granite-transformations-of-northeast-ohio/?utm_source=Yelp&utm_campaign=2018', 'http://www.greentreefootandankle.com', 'https://medmen.com/stores/las-vegas-the-strip-paradise-and-harmon/', None, None, None, None, None, 'http://www.paradisehalls.com', 'http://www.jamrockcafe.com', None, 'http://www.ocadu.ca/', 'http://www.bathandbodyworks.com', 'http://www.hollywoodtans.com', 'http://gehomeservicesllc.com', 'http://eosfitness.com/location/peoria?utm_campaign=peoria&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', 'https://www.firehousesubs.ca', 'https://nationwidevision.com/locations', 'http://www.doubledspizzas.com', 'http://www.waxandlash.ca', 'https://www.tidesonthomas.com', 'http://l.macys.com/superstition-springs-center-in-mesa-az?cm_mmc=Yelp_Stores-_-Mesa-_-n-_-459&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Mesa_459&m_ac=yelp_stores&m_ag=n', 'http://fiveguys.com/', None, 'http://www.fastlanecoatings.com', None, None, None, None, 'http://peignedancestudios.com', None, 'http://www.scottsdalesilveradogolfclub.com/', None, 'http://www.fithcc.com', 'https://tattoocorner.business.site', None, 'http://www.fransrestaurant.com', 'http://www.thelittleclinic.com', None, 'http://www.copperstatehandymanservices.com', None, 'http://www.soniasbridalstudio.com', 'http://sollidcabinetry.com', 'http://www.dukephototempeaz.com', None, 'http://www.city.cleveland.oh.us/CityofCleveland/Home/Government/', '1592185371', 'http://www.saukpointvet.com', 'https://www.duckdonuts.com/location/orange-village-oh-2/', 'https://www.starlitebbq.com', None, None, 'http://www.tartucollege.ca/', 'http://sanctuary-salon-spa.com', None, 'http://www.swignsweets.com', 'http://englishbayfish.ca', 'http://www.riderta.com/facilities/airport', None, 'http://www.arbys.com/', '1592185397', 'http://northmesaauto.com', None, 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'https://www.phillipslaw.com/phoenix-arizona-personal-injury-lawyers', 'http://www.momdocwfw.com/estrella', 'https://thelearningexperience.com/preschoolsuccess?utm_source=Yelp&utm_medium=Referral&utm_campaign=Sponsored+Business+Listings', 'http://www.harveyspaint.com', 'https://www.screensunlimited.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.bombayexpresstoronto.com/', None, 'http://www.dominos.com', 'http://www.beautyavenue.us', 'http://www.thethirdestimate.com/', None, None, 'http://1stchoicemechanicalaz.com', 'https://redrock.sclv.com/Dining/Grand-Cafe?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.glockmeister.com', 'http://greenjadechampaign.com', None, '1592185448', None, 'https://escapetheroom.com/phoenix/', None, 'http://www.atthebarns.org/', 'http://www.thebagelcafelv.com/', None, 'http://www.spicypickle.com/restaurants/arizona.html', None, None, 'http://www.dollarama.com', 'http://www.aaaactiondoors.com', None, None, None, 'http://www.lobtoronto.com', 'http://www.happyspizza.com', 'https://locations.comerica.com/location/75th-thunderbird', None, 'http://servitaxlv.com', 'http://www.azdot.gov/mvd', 'http://www.perinatal.com', 'https://www.imagedentallasvegas.com/?utm_source=yelp&utm_medium=link&utm_campaign=yelp', 'http://www.pghoptical.com', None, None, 'https://www.mckenziesmidtown.com', 'http://www.redsearestaurant.net', 'http://www.mallorcarestaurant.com', 'http://broadviewbeauty.ca', 'https://www.homecitybnb.com', 'https://local.fedex.com/oh/bedford-heights/LNNA/', 'http://www.guschaletrestaurant.com', None, 'http://www.tinyboxvapeshop.com', 'http://www.barrettfinancial.com', '1592185518', None, 'http://www.delanolasvegas.com/en/nightlife/skyfall-lounge.html', None, '1592185526', None, None, 'http://www.openarmspreschool.ca', 'https://www.jerseymikes.com/9004', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', 'http://www.phoenixfamilymedical.com/', 'http://www.capitaldrip.com', None, None, 'http://www.handelsicecream.com', None, 'http://www.kaleidoscope-living.com', '1592185552', 'http://www.head2toechiro.com', 'http://www.eastvalleyfloors.com', 'http://www.scrapbookbarngilbert.com', None, 'http://www.nextcare.com/locations/az/peoria-glendale/?utm_source=Yelp&utm_medium=Local&utm_campaign=peoria_glendale', 'http://www.relaxologywellness.com', 'https://theoaksevents.com', 'http://www.imsiamlasvegas.com', None, 'https://www.restaurantohsushi.com', 'http://www.troplv.com/meetings-and-events/havana-room', None, 'http://www.lvms.com/bullring', 'http://www.antoniospizza.net', 'http://arbortrimming.com', None, 'https://www.venetian.com/towers/the-palazzo.html?utm_source=yelp&utm_medium=partner&utm_campaign=businesslisting', None, None, 'http://www.rajdhanisweets.ca', 'http://www.cashmanphoto.com', None, None, 'https://agent.amfam.com/nv/north-las-vegas/colleen-drinnon/', 'http://www.grandtouringautos.com/', 'https://locations.wendys.com/united-states/az/laveen/3520-w-baseline-road', 'http://www.fuzesalon.ca', 'http://gerchickrealestate.com/', 'https://greenvalleyranch.sclv.com/?utm_source=YELP&utm_medium=SOCIAL&utm_term=GVR&utm_content=GVR-PROPERTIES&utm_campaign=GVR-YELP', 'http://hamptoninn3.hilton.com/en/hotels/ontario/hampton-inn-by-hilton-toronto-airport-corporate-centre-YTOSOHX/index.html?SEO_id=YELP-HP-YTOSOHX', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.everythinginsight.net/our-practice.html', None, None, None, None, None, 'http://www.petco.com', 'http://www.willietys.com/', 'http://www.sidebarphoenix.com', None, None, 'http://www.pandahobby.store', 'https://dealer.sprint.com/experts-choice', 'http://illinishuttle.com', None, 'http://www.instylenail.ca/', 'http://www.mcdonalds.com', 'http://www.clhairartstudio.com', None, None, None, 'http://www.garciaswm.com/', None, 'https://locations.einsteinbros.com/us/az/surprise/13746-w-bell-rd', 'http://www.michaelsbridalgalleria.com', 'http://www.penn-station.com', 'http://www.prmvineyards.com', 'http://Mindbodysoles.net', 'http://EvansLasVegas.com', None, None, None, 'http://www.carolinavaluevillage.com', 'https://locations.whataburger.com/az/scottsdale/2955-n-hayden-rd.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', 'http://www.coolclubs.com', 'http://Azkickbacktours.com', 'https://www.phoenix.gov/parks/sports/complexes/desert-west', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.trilliumweightloss.com', 'http://www.runningwiththebullsusa.com', 'http://saporebyzafferano.ca/', None, None, 'http://www.thehkan.com', 'http://www.hayleylynnedoeshair.com', None, 'http://www.cotswoldfarmersmarket.com', 'http://www.kaleidoscopejuice.com/', 'http://www.harrysgrilleandtavern.com', None, 'http://local.biglots.com/az/gilbert/1913?zcp=pd_local_yelp', 'http://www.scottsdaleobgyns.com/russellBartelsMD.html', 'http://www.yourcarinsiders.com', 'https://www.supercuts.com/locations/pa/pittsburgh/shadyside-plaza-s-highland-haircuts-8953.html', '1592185734', None, None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.yknotparty.com', None, None, 'http://local.firestonecompleteautocare.com/ohio/north-olmsted/4580-great-northern-blvd/?lw_cmp=IYP_YPC_MLP_14796', 'https://www.saksfifthavenue.com/locations/s/sherwaygardens', None, None, 'http://www.vintagehomecharlotte.com', 'http://Www.aglowbeautybarlv.com', 'http://www.carolinaherrera.com', None, 'http://www.activegreenross.com', None, None, 'https://locations.whataburger.com/az/mesa/1947-w-broadway-rd.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', None, None, 'http://locopatron.com/', 'http://livewellmassage.vpweb.com', None, 'http://www.mammaspizza.com', 'http://www.victoiredayspa.ca', 'http://www.outback.com/locations/nv/las-vegas-craig', 'http://bandnautosalesllc.weebly.com', 'http://us.shop.ecco.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://firenzastone.com/', None, None, 'http://auxiliarycrossfit.com', 'http://www.capitolpetroleumllc.com/site/', 'http://www.pogllc.com', None, None, 'http://www.legendscafelv.com', 'http://www.sweetlifegelateria.com', 'http://www.clutchlandscaping.com', 'https://www.lesinsulaires.ca', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', 'http://mine-sushi.com/', '1592185823', 'http://www.tsingtaomesaaz.com', 'http://www.Friendly-Wireless.com', 'http://www.bmvbooks.com/', 'http://www.smoochiepoochiedoggrooming.com', 'http://www.LaurenParis.com', 'https://www.wyndhamgardencalgaryairport.ca', None, 'https://www.calgarycoop.com/stores/shawnessy/', None, None, 'http://bosadonutsaz.com', 'https://www.ganleylincolnohio.com', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/brampton-7688-hurontario-street.aspx?postalcode=L7A+3R9&storeid=66', None, 'http://www.thestratford.org/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', None, 'http://www.eddiebauer.com', 'http://www.tempritelv.com', None, 'https://www.saksfifthavenue.com/locations/s/phoenix', 'http://www.carolinavet.com/locations/matthews-nc/', 'http://aestheticbodycontouring.net', None, 'http://www.ganleysubaru.com', 'https://vbarbershop.com/location/chandler-fulton-ranch/', 'http://www.bellanailshop.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://hashtaggallery.com', 'https://locations.theupsstore.com/nc/matthews/2217-matthews-township-pkwy?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Henderson-NV-89011/807058/', 'http://www.heislersmarket.com', '1592185901', None, 'https://www.esso.ca', 'http://www.hogwildpitbbq.com', None, None, '1592185915', 'https://www.kohls.com/stores/az/glendale-652.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.indiasflame.com', 'http://www.brightoncollisioncenter.com/', None, 'http://workoutquest.com', 'http://www.eagerbeaverplumbing.com', 'http://allens-pool-catering.business.site', '1592185934', 'http://www.ostlerfamilydental.com', 'https://chutneyb.com', 'http://www.ae.com', None, 'http://vspconsignment.com', 'https://www.zipscarwash.com/location/rock-hill-sc/', 'http://www.teresaspizza.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.morphebrushes.com', None, 'http://schwans.com', 'http://lovekimnailsspa.wix.com/home', None, 'http://www.earthangelsholistic.com', None, None, 'http://8thwonderstudio.com', 'http://www.bowtiepizza.com', None, 'http://www.eggsmart.ca', None, None, 'http://www.chapters.indigo.ca/home/storelocator/storeDetails/929/', 'http://www.donvalleyvw.net', 'https://druxys.com/location/2-st-clair-ave-colonia-place/', 'http://www.aemediaproduction.com', 'http://www.wingmachine.com', 'http://www.lvmis.com', None, 'http://www.vegaspubcrawler.com', None, 'http://www.jeromesalon.com', 'http://www.transformerstation.org/', 'https://lasvegas.adamevestores.com', 'http://www.dvtowing.com', None, None, 'http://Longevityinfitnessexcellence.com', 'http://www.smilebeautifuldentistry.com', 'http://www.marriott.com/hotels/travel/yyzap-courtyard-toronto-airport', 'http://www.urbanbloomcurls.com', 'https://www.willowpark.net', None, 'http://local.biglots.com/az/phoenix/4085', None, None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://rogersandhollands.com/east-towne-mall', 'https://starliterestaurant.ca', 'https://texasstation.sclv.com/Dining/Slices-Pizzeria', 'http://www.oldmillgm.ca', None, 'http://www.maac.com/alabama/huntsville/colonial-grand-at-madison?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://www.drbarbaranewman.com', 'http://www.clecabinets.com', None, 'http://www.mcmagain.com/home.html', 'https://locations.theupsstore.com/nc/charlotte/2820-selwyn-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.bloorfitness.com/', 'http://www.kouskousexpress.com', None, 'http://www.sweetalamode.ca', None, None, None, None, 'http://www.globalpestlasvegas.com', None, 'http://www.foliclesalonandspa.com/', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.givemiacookie.com', 'http://www.chatime.com', 'http://www.therobotoproject.com', 'https://www.bushmillsirishpub.com', 'http://ladlows.com', 'https://sfaservice.com', None, None, 'https://luxxestudio412.glossgenius.com', 'http://www.alankells.com', 'http://www.gianteagle.com/store-locator', 'http://www.marytripi.com', 'http://rajplasticsurgery.com/', None, 'http://www.deltaco.com', 'http://www.steelcitysteak.com', 'http://nickelsdeli.com/saint-laurent/', None, 'http://momentumsalon.com', 'https://octapharmaplasma.com/donor/center/18568', 'http://www.mastercleaners.us', 'http://www.justfresh.com', None, 'https://www.gowireless.com/stores/az/phoenix/phoenix-ahwatukee-foothills/', 'http://shop.helixtelecom.com/', 'http://www.CerberusDesigns.ca', 'http://www.betsysicecream.com', 'https://www.newyorknewyork.com/en/nightlife/pour-24.html', 'http://pinogelato.com', None, 'http://www.vergerlacroix.ca/', 'http://www.starbucks.com/store/113209/', 'http://www.alexreidosleitoes.com', 'http://www.habitatlivingsound.com', 'http://www.attackpestcontrollv.com', 'https://www.kindercare.com/our-centers/mesa/az/000632?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=000632', 'http://www.pawsplaygrounds.com', None, 'http://www.zagg.com', 'https://www.donmillersubaruwest.com', None, 'http://www.ArcadiaCoveApartments.com', None, 'http://www.bodyheattanning.com', 'http://www.litespressobar.com', 'http://www.barbiespetsitting.com', 'http://www.hungryhut247.com', 'http://www.restaurantmochica.com/en/toronto', '1592186182', None, 'http://www.evoautoaz.com', '1592186188', 'http://phochay88.com', None, 'http://www.rockyscustomdetailing.com/', 'http://www.azeyes.com', 'https://www.therackandcue.com', 'http://www.backdoorlv.com', None, 'https://www.capriottis.com', None, 'https://lemonsharkpoke.com/locations/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://www.usps.com', 'https://www.labcorp.com', None, None, 'http://www.omzhair.com', 'https://www.marcs.com/stores/marcs-middleburg-hts-southland-grocery-store-4413', None, 'http://woodsrestaurant.ca/', None, None, None, 'http://fourpalmsautosales.com', 'http://gesu.com/', None, 'https://www.purdys.com/shops/details/79', 'http://www.scilv.com', 'http://tjsbutcherblock.com', 'http://aquatherapyclinics.com/', 'https://locations.costavida.com/costa-vida-a2660367671e', 'http://ragingspoon.ca/', 'http://www.queenfishandchips.com/', 'http://www.brownleejewelers.com', '1592186258', 'http://www.gypsybarphoenix.com', 'http://www.tbsstrong.com', 'http://www.titanrelocationservices.com', 'http://www.majormilliken.com/', 'http://www.bestautobuy.com/', 'http://Www.GotGoddessHair.com', 'http://www.cleatswings.com', 'http://outpostcoffee.com', None, None, 'http://www.ampm.com', 'http://www.photoantiquities.org', 'http://www.atmosphere.ca/', 'http://affordablelakenormanshuttle.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'https://stores.mooresclothing.com/ab/calgary/415---3545-32nd-ave--ne.html?utm_source=yelp&utm_medium=listing&utm_content=41&utm_campaign=AB', 'http://www.disciacca.com', None, None, None, '1592186300', 'https://sparklenailsbar.com', 'http://southpointcasino.com/dining/michaels-gourmet-room?cid=ypmic', 'http://www.fiveyearsyoungerfacial.com', 'http://www.thecrepecafe.com', 'http://locations.harristeeter.com/nc/charlotte/205/', None, 'http://www.JohnsonEstateLaw.com', 'http://walmart.com/', None, None, None, 'https://www.pizza73.com', 'https://www.batteriesplus.com/store-locator/az/tempe/batteries-plus-333?utm_source=yelp&utm_medium=local&storecode=333', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', None, '1592186333', 'https://dwss.nv.gov', None, None, 'http://noftz.com', 'https://santanvillage.benefitbrowbars.com', '1592186344', 'http://www.cardiacsolutions.net', 'http://natureworksbest.com/', 'http://www.mdclv.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://www.petsmart.com', None, None, 'http://www.sawhilbanquet.com', 'https://lernerandrowe.com/?utm_source=Yelp', 'http://www.maccosmetics.com', None, 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', 'http://www.timhortons.com', None, 'https://www.rolex.com/rolex-dealers/dealer-locator/retailers-details/rolexboutiquelvluxury.rswi_17986.lasvegas.unitedstates.rolexdealers.com', 'http://www.vosgeschocolate.com', 'http://www.a2zrm.com/', None, None, 'http://www.pittsburghprestigephotobooth.com', 'http://www.carmeldayspa.com', 'http://reddiservices.com/phoenix', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.abcpediatricshenderson.com/', 'http://www.wolsteincenter.com', 'https://stores.chicos.com/s/the-summit-at-scottsdale', 'http://www.monsterpgh.com', 'http://www.soccerzonevegas.com', 'http://www.northhillpizza.com', 'http://www.oxigenspa.com', None, 'https://eyetique.com/squirrel-hill', None, 'http://www.azresearchcenter.com/', '1592186416', 'https://www.cielohendersonapts.com', 'http://www.baileyorthoaz.com/', 'http://www.hobbypeople.net', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=clesv&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'https://mandarinrestaurant.com/mississauga/', 'http://www.switchconsignment.com', 'http://www.porschenorthscottsdale.com', 'http://www.carolinapacknc.com', None, None, 'http://www.guyandgalsalongilbert.com', '1592186443', 'https://www.wilhelmautomotive.com/locations/tatum-ranch/', None, None, 'https://twomenandatruck.com/movers/il/champaign', 'https://castlerents.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'http://www.dukescycle.ca', 'http://greatwhaletattoo.com', '1592186463', None, 'http://www.trilliummoving.com', None, 'https://www.dominos.com', 'http://local.buckle.com/AZ/TEMPE/385/?utm_source=Buckle&utm_medium=Website&utm_campaign=Store+Locator', 'http://myorangeleaf.com/frozen-yogurt-store/AZ/chandler/2875-west-ray-rd%2c-suite-1?id=8', 'http://www.17thavechiropractor.com', 'http://www.abiaz.com', 'http://www.thevenetian.com/RIVA.aspx', '1592186483', None, None, 'http://vwnorthscottsdale.com', '1592186491', '1592186493', 'http://www.gordsappliance.com', 'http://www.robinsongarden.com', 'http://www.cityandeast.com', 'http://ccvet.com', 'http://www.treatmentsalon.com', 'http://www.cottonon.com', 'http://fixauto.com/scarborough-town-centre', None, None, 'http://www.whitetoronto.com/', 'http://www.ercfixtv.com', 'http://www.jimmyscoffee.ca', 'http://www.ngvlanes.com', 'https://www.anytimefitness.com/gyms/288/Las-Vegas-NV-89139/?utm_source=yelp&utm_medium=local', 'http://inandoutmoving.ca/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.madisonavecakes.com', 'http://www.manestudio.ca', 'http://blackcatpgh.com', None, 'http://www.smileshopdental.com', 'https://www1.shoppersdrugmart.ca', 'http://www.bullfrogspas.com', 'http://www.childrenslearningadventure.com/', None, '1592186547', 'http://www.desimoneglobalmarketing.com', '1592186550', 'http://www.timetoronto.com', 'http://restaurant.chineseonlineorder.com/goldengatehenderson', 'http://restaurantletandoor.ca', 'https://www.autozone.com/locations/az/phoenix/3908-e-thomas-rd.html', 'https://www.snapdragon-salon.com', 'http://www.thetamalestore.com', 'http://www.peterpiperpizza.com/', None, 'https://mononabarbershop.com', 'http://www.carolinasdish.com/', 'http://www.sparkleanlaundryphoenix.com/', 'http://www.lagunaspanv.com/', None, 'http://www.foxfamilydental.net', None, '1592186583', 'http://www.usps.com', 'http://www.sprint.com', None, 'http://islandheatdinnershow.com', 'http://flashforwardsites.com', 'http://www.bishoplawoffice.com', 'http://www.grandavenueproduce.com', '1592186601', 'http://www.balconycleaning.net', 'https://www.mapleteahouse.com', None, '1592186607', 'http://www.thechesterfieldshop.com', None, 'https://cftn.com', 'https://stoughtontireandautorepairinc.com', 'http://www.jiffylube.com', 'http://www.starbucks.com/store/9298/', 'http://www.thaidelightaz.com', 'https://www.redmountainweightloss.com/scottsdale/', 'https://www.libertysquare-apartments.com', '1592186628', 'http://guireitoronto.com', '1592186632', None, 'http://k1speed.com/phoenix-location.html?utm_source=Yelp', 'http://www.jasesouder.com', 'http://www.thecalgarygroomroom.com', None, 'http://www.littleones.ca', 'http://www.leagueofvapes.ca', 'http://www.scottsleedmd.com', None, 'http://mex-city.com/', None, 'http://www.azrapidmaintenance.com/index.html', 'http://www.coveredwagonaz.com/', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, 'https://www.thepaincenter.com/?utm_source=yelp&utm_medium=referral&utm_content=arizona-gilbert', 'http://ritzasiaaz.com/location.php/', 'http://www.meineke.com', 'http://www.soraonrose.com', None, 'http://www.ritzcarlton.com/en/hotels/canada/toronto', 'http://paradisevalleyseptic.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357318&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://torrancepharmacy.com', None, 'http://www.littlecaesars.com', 'http://www.hummusbowls.com', '1592186689', 'http://www.audioworkx.com/', 'http://restaurantvago.com', None, 'https://www.batteriesplus.com/store-locator/nc/gastonia/batteries-plus-423?utm_source=yelp&utm_medium=local&storecode=423', 'https://beezybooth.com', 'https://www.montecarlo.com/en/nightlife/brand-lounge.html', None, 'http://www.sovarizona.com', 'https://www.orangetheory.com/en-us/locations/arizona/phoenix/2501-west-happy-valley-road-suite-32-1020/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.stylevsalon.com', None, 'https://www.ahn.org/location-detail?name=AGH_Suburban', 'http://shopurbo.com', 'https://www.josbank.com/store-locator/mt-lebanon-pa-356?utm_source=yelp&utm_medium=listing&utm_content=356&utm_campaign=PA', 'http://www.campers-village.com', None, 'http://www.bouldercreekgc.com', None, None, None, 'http://www.bigalscanada.com/stores/locations/NorthYork/northyork.html', '1592186732', None, 'http://www.oakdalepodiatrist.com', 'https://www.penrosecharlotte.com', None, 'http://www.wildwingrestaurants.com/franchisees/brampton-trinity-commons/', 'http://www.scottsdalehillsah.com', 'https://www.sundancecinemas.com/', '1592186748', None, None, None, 'http://www.opticgallerysummerlin.com', None, 'http://www.cottonlanervresort.com', '1592186762', 'http://franklygoodcoffee.com', '1592186767', 'http://www.thebeerstore.ca/locations/sheppardwillowdale', 'https://www.moxieservices.com/locations/phoenix/?utm_source=yelp&utm_medium=cpc&utm_campaign=2019_cpc', 'http://www.valleymedped.com', None, '1592186777', 'http://www.camelotinnelyria.us', 'http://www.kevinpowellmotorsportscharlotte.com', None, 'http://www.spiceasianbiz.com', 'http://www.santabarbaracatering.com', 'https://www.gamestop.com/store/us/wi/madison/740/prairie-towne-center-gamestop', 'http://www.lasvegasspinesurgeon.com', 'http://songbirdartistry.com', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', None, 'https://budgetblinds.com/Goodyear/?utm_source=yelp&utm_medium=naf-listing&utm_campaign=NAF-LOCAL-YELP', None, None, 'https://www.amazinglashstudio.com/studios/nc/charlotte/park-towne-village', None, 'http://www.therollhouse.com/wickliffe', 'http://www.dunkindonuts.com', 'https://www.purebarre.com/location/chandler-az', None, 'http://www.eliteacademyofgymnastics.com', 'http://advancedmetal.com', 'http://www.pitaland.ca', None, 'http://www.evex.ca', None, None, 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', None, 'https://aamcobayarea.com/locations/concord', 'http://www.starbucks.com', 'http://www.spectrumbrands.com/', None, 'http://www.bellybumpsandbabies.com/', None, 'http://www.theknittingroom.ca', 'http://www.simplesimonpies.com', 'http://www.ohiojunkforce.com', None, 'http://www.publix.com', '1592186858', None, 'http://www.furniturestorelasvegas4u.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://tumbleweedhotel-hub.com/', None, None, 'http://www.polishdnailbar.com', 'http://uppercrustwinebar.com', 'https://www.kfc.ca//store/1595-cote-vertu-st-laurent', None, None, None, 'http://www.25liberty.ca', 'http://www.yehyogourt.com/', 'http://www.lasvegasfloral.com/?srccode=EF_YELP', 'http://www.wigsrustoronto.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'https://ramclean.com', None, None, 'http://mintlocker.com', None, None, 'http://www.greenfieldgroomingsalon.com', None, '1592186914', 'http://www.tankstap.com/', None, 'http://www.ouestantoniospizza.com', 'http://www.badwaterbrewing.com', 'https://local.albertsons.com/az/chandler/3145-s-alma-school-rd.html', None, None, 'https://quantumcleaning282.wixsite.com/website', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd', None, 'http://www.milestonesrestaurants.com/', None, None, None, 'http://www.wmdouglas.com/charlotte', 'http://www.nvscc.com', None, None, 'http://www.planetdog.ca', 'https://www.arizonarestorativepsychiatry.com', None, None, 'http://www.mevamekitchenexpress.com/', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', None, 'http://nevadaeyephysicians.com', 'http://www.ranchorelaxotogo.com', 'https://hakkasan.com/las-vegas/', 'http://www.dysartdental.com', 'http://stacyannsscissorhands.com', 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', 'https://locations.churchs.com/nv-las-vegas-8616', 'http://www.landmarkautoanddiesel.com', 'http://www.familyvideo.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://stores.dickssportinggoods.com/az/scottsdale/1194/', 'http://www.drallenhuioptometry.com/', 'http://www.fabfred.com/locations/ft-apache/', 'http://www.theteakeeper.com/', 'https://agents.allstate.com/juan-deglane-glendale-az.html', 'http://www.ctctree.com', 'http://www.saharaair.com', None, None, None, 'http://www.holtrenfrew.com/store/holt/stores/hr2/VaughanMills', None, 'http://www.bennett2rentit.com', 'https://locations.theupsstore.com/az/scottsdale/16211-n-scottsdale-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=11088&localechange=1', '1592187020', 'http://www.auburnbayvet.com', 'https://www.swiftaviation.com', 'http://www.sundevilauto.com/locations/az/scottsdale/north-scottsdale-25', None, None, 'http://www.pinotspalette.com/southend', 'http://www.pinkynails.ca', 'http://smartrepairsaz.com', 'http://www.lizyhoeffer.com', 'https://www.spiritsandtales.com', '1592187046', 'http://www.greatclips.com/salons/4614', 'http://www.dunkindonuts.com', None, None, 'http://walkinwalkin.com', None, '1592187060', None, None, None, 'http://www.seespotclean.com', 'http://gogreenac.com/', 'https://iworkoncars.com', 'https://silvernuggetlv.com', None, 'http://www.bk.com', 'http://www.mgmgrand.com/restaurants/crush.aspx', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FMSNMW', 'http://www.AbsolutePetCareAZ.com', 'http://www.scrubtastic.com', 'http://broadbentdentistry.com/', 'https://www.bestbuy.com/site/electronics/geek-squad/pcmcat138100050018.c?id=pcmcat138100050018', 'http://www.honmachirestaurant.com', 'http://www.bluearrowrecords.com/', 'http://www.phoenixrackandaxle.com', None, 'http://www.parkcentraldeli.com', None, 'https://www.mygabes.com', 'http://thriftdlux.com/', None, 'http://www.clinicsalveo.ca', 'http://www.pandora.net/en-us/stores/united-states/85254/pandora-scottsdale-quarter', None, 'https://www.sprint.com/storefronts/bd/sprint-north-las-vegas-nv-89032-fcs-4123/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.housemaster.com', None, None, 'http://nodabarkandboard.com/home.html', 'https://www.destinymartialartsacademy.com', 'http://emakravmaga.ca', 'http://www.stateoftheartdesigners.net', 'https://www.chevronwithtechron.com', 'http://www.bigjimsrestaurant.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=626&utm_content=bpas', None, None, 'https://www.lasikvisioninstitute.com/lasik-eye-surgery/cleveland-surgeon-center/?venid=YLP31&subid=CLE', None, '1592187147', None, 'http://www.verizonwireless.com/stores/arizona/mesa/val-vista-204086/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://www.midwoodsmokeshack.com', 'http://www.chapters.indigo.ca', 'https://www.vistasureno.com', 'http://www.therumormillmarket.com', 'http://www.drywallperfection.com', '1592187163', 'http://artscapeyoungplace.ca', 'https://www.supercuts.com/locations/oh/rocky-river/rocky-river-haircuts-81630.html', 'http://www.katieskorner.com', 'http://www.camh.net', 'http://www.southwestfunctionalmedicine.com', None, None, 'http://www.lionsmanegrooming.com', 'http://www.amazinginc.net', 'https://haircutmenfairlawnoh.com', None, 'http://www.cherryberrieslasvegas.com', 'http://www.shopwoc.com', 'https://www.amcofdv.com', 'http://www.starbucks.com/store/10759/', 'http://usmaniagrill.ca', 'http://www.igoturback.com?cmpid=GSDG_BLM_0006', 'http://www.cal-am.com/communities/chaparral-village', 'http://azmajorsoccerleague.com', None, 'http://www.valleygoldmine.com', 'http://www.saludjuicery.com/aspinwall/', 'http://www.undefeated.com', None, 'http://www.whatalesya.com', 'https://www.burialplanning.com/cemeteries/resthaven-memory-gardens/', 'http://collegestreetanimalhospital.com', 'http://pueblosereno.com/', 'http://www.autonationbuickgmchenderson.com', None, 'http://fortmill.burnbootcamp.com/', 'http://www.orangedumpster.com/', 'http://portofsubs.com', 'https://www.newdermamedlaserclinic.com', None, None, 'http://www.svmmjcc.com', 'https://stores.bareminerals.com/wi/madison/us-2313/', None, 'http://www.rdquake.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.sears.com', None, 'https://www.storage-solutions.org/storage/arizona/storage-units-peoria/8266-W-Lake-Pleasant-Parkway-115', 'http://www.darinaelectrolysis.ca', 'https://www.allamericanpubclt.com', 'http://www.sasshoescharlotte.com', 'http://taylormadecustompools.com', 'http://www.kitchen73.ca/laval', 'http://colorworkslandscape.net', 'http://www.bodyrestorationmassage.com', 'http://fujiyamacalgary.com', 'http://www.castleapartments.net', 'https://www.myeyedr.com/locations/independence-boulevard?utm_source=Yelp&utm_medium=Referral&utm_campaign=independence-boulevard', 'http://carlretterdebtattorney.com', None, 'https://zelaya-jr-painting.com', 'http://www.swarovski.com/Web_CA/en/index', 'http://www.trapezeu.com', None, 'http://www.marshallsonline.com', 'http://kokofitclub.com', 'https://www.thirdfederal.com?=ad.doubleclick.net/ddm/clk/458420725;262568795;w', 'http://www.tropicalsmoothie.com', 'http://www.jonesysclassiccleaners.com/', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', None, 'http://tradelandsaz.com', None, 'http://www.sweetfixbakery.com', None, 'https://www.cellphonerepair.com/charlotte-university-city-nc/', 'http://www.happyvalleyplumbingllc.com', 'http://www.oneofakindpets.com/', 'http://jacksonswash.com', None, None, 'http://www.talkingstickresort.com/spa.aspx', 'http://nathansfamous.com', 'http://fiveguys.com/', None, None, None, None, 'http://christensenconstruction.net', '1592187329', 'http://www.realliving.com/sj-fowler-real-estate', 'http://www.gnargnartours.com/', None, 'http://www.apachestone.com', 'http://www.doddsdoors.com', 'http://www.subway.com', 'http://www.canyon-pt.com/location/surprise-office/', 'http://trustarts.culturaldistrict.org/production/37630', None, 'https://stores.savers.com/nv/lasvegas/savers-thrift-store-1047.html', 'https://milk-n-more.business.site', None, 'http://www.sfldentistry.com', 'https://extremewheels.com', None, 'http://www.JimmyJohns.com', None, None, None, 'https://www.thehouseofused.com', 'http://www.nhhuntersvillepedsandim.org', 'http://www.origintmassage.com/', None, 'http://www.hskaraoke.com', 'http://mesa.floorstogo.com', 'http://www.nveyesurgery.com', 'http://www.stoutflooring.com', None, None, 'https://square.site/book/0GPTRC4PSJ0WB/sunny-girl-spray-tan-phoenix-az', None, 'http://www.leanonmeals.ca', 'http://www.colossusgreektaverna.com/locations/colossuspc/contact/', 'http://sonoranserenityspa.com/', '1592187400', 'http://www.blm.gov', 'https://thrifty.com/loc/ll/CA/OT/TORONTO-~-FRONT-ST-(OT)/330-FRONT-STREET-WEST', 'http://www.benchworksteering.com/', 'http://visit.brownmackie.edu/SERCH/dynamic/bmc-3-step.aspx?RIFID=3322&source=YELP&sourceCode=YELP&cid=SERCH_BMWA_096_SRCH_002&SearchEngine=Yelp&utm_source=Yelp&utm_medium=cpc&utm_campaign=Yelp', None, 'http://www.suzannewigginton.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.carepatrol.com/', '1592187418', None, None, 'http://artgeckoshop.com', None, None, None, 'http://www.loftsonthomas.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/pa/turtle-creek-4072.html?mcid=iyp:8368400', None, 'http://www.thebierhausbistro.com/', 'http://www.wheatbyjay.ca', None, None, None, '1592187446', '1592187449', None, 'http://brathausaz.com/brat-haus-events/', None, 'http://www.stardustbuilding.org', None, 'http://www.blackcanyonconferencecenter.com', 'http://www.pittsburghyellowcab.com', None, 'http://www.casbahrestaurant.ca', 'http://www.solosmallmotors.ca', 'http://www.empirepizzabar.com', 'http://www.jacksonswash.com/location-84th-avenue', 'http://www.dakinemobiledetailing.com', 'http://www.adrenalinetoronto.com', 'http://www.drlockney.com', 'https://locations.churchs.com/az-phoenix-681', 'http://venues.calgarystampede.com/venues/bmo-centre/', 'https://bikanersweetsandrestaurant.ca', '1592187485', None, 'http://www.prayosha.ca/', None, 'http://blackcanarycoffee.com', 'http://www.massagewellvegas.com', 'http://www.brookdaledentalcare.com', 'http://www.mcdonalds.com', None, 'http://www.customcaninecompany.com', 'http://www.dcslv.org', None, 'http://www.terribleherbst.com/', None, None, None, None, 'http://gocheckers.com/team/game-guide', 'http://paradisemelts.com', 'http://www.tribebarrestudio.com', 'http://www.fuguasian.com/menu.aspx', None, None, 'http://www.billygrahamlibrary.org', 'http://www.purolator.com/purolator/ship-track/find-location.page?location=ridRC0715', None, 'http://www.fedex.com', None, 'https://www.snwa.com', 'http://www.freshandeasy.com', None, 'http://www.orthopaedicspecialists.org', None, 'https://www.kwiktrip.com/Locations/Details/650', 'http://www.phoenixbedbugexpert.com', None, 'http://www.videoconversionexperts.com/', 'https://www.cash1loans.com/locations/arizona/phoenix-thomas.aspx', 'http://local.firestonecompleteautocare.com/ohio/cleveland/6874-pearl-rd/?lw_cmp=IYP_YPC_MLP_1694', 'http://www.canadiantire.ca/en/store-details/on/warden-eglinton-on.store.html', '1592187562', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://supremetouch15.wixsite.com/supreme-touch/contact', 'http://www.perryellis.com?utm_source=Yelp&utm_medium=Social&utm_campaign=PE_Yelp_BioCTA', 'http://www.mrtire.com', None, 'http://www.sunbirdgolf.com', None, 'http://www.mocca.ca', 'https://www.pizzaville.ca/stores/hours/2889-derry-road', None, 'http://www.maranellocafe.ca', 'http://www.torontosteamnclean.ca', 'http://www.jogoyaseafoodbuffet.com/', None, 'http://www.joefresh.com', 'http://ladolcepesca.com', 'https://www.theshadestore.com/showrooms/nevada/las-vegas?utm_source=yelp&utm_medium=cpc', 'http://www.tristatetowingandrecovery.com', None, '1592187599', 'http://www.royalvinewinebar.com/', None, 'http://SecondsCity.com', 'http://www.ljsilvers.com', None, 'http://scacciaunion.ca', 'http://truhitfitness.com/north-phoenix/', 'https://orlandoautobody.com', 'http://www.coyoteoaties.com', 'https://www.jiffylube.com/locations/az/phoenix/2098', 'http://www.bigmanspizza.ca', 'https://www.dogtrainer-charlotte.com', None, None, 'http://www.goodwillaz.org/location/goodwill-mckellips-mesa/', 'http://www.azspinalcare.com/', 'http://www.ranee.ca', 'http://www.thecornflower.com', 'http://www.springspreserve.org', None, 'http://www.dakotamoversaz.com', None, '1592187645', 'http://www.bownesshealthfood.ca', 'https://rapidresponders.com', None, 'https://amazingleakdetection.com', None, 'http://www.midas.com/cleveland/store.aspx?shopnum=6355&dmanum=212', 'https://www.fountainpalmsapts.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', 'http://www.bojangles.com', 'http://www.themagicshoplv.com', None, 'http://www.sewmuchfun4you.com/', None, 'http://www.hickorynutgolfcourse.com', 'http://www.mrsbridalboutique.com/', 'https://www.harveys.ca', 'http://www.AZLawnGuys.com', '1592187676', 'https://www.spencediamonds.ca/location/calgary-ab/?utm_source=Yelp&utm_medium=Display', 'http://www.LasVegas1RealEstate.com', None, 'http://www.samosafactory.com', 'http://www.thebrubakerspub.com', None, 'https://www.homestreet.com', 'http://www.nikosgardening.ca/', None, 'https://www.victra.com/?utm_content=Yelp&utm_medium=URL&utm_source=Yelp', 'https://www.mindbodhiyoga.com', 'http://www.virginamerica.com/', None, None, 'http://www.health-a-licious.com', 'http://lacampagnaonline.com', 'http://www.canampm.com/sun-valley-ranch', 'http://www.ranefamilyinsurance.com', None, 'https://stores.nyxcosmetics.com/directory/nv/las-vegas/3663-south-las-vegas-blvd.html', 'http://trilogycle.com', None, 'http://www.bloomersto.com', 'https://www.walmart.com/store/5334/aurora-co/details', 'http://www.fithcc.com', None, 'http://99only.com/store/Las-Vegas---Beltway/', '1592187730', None, 'http://www.vbinspect.com', 'http://www.makinolasvegas.com', None, 'http://samspizza.co', 'http://www.swimmerinsurance.com', 'http://www.lipsboutiquebyjka.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.themarvelexperience.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.bannerhealth.com/locations/banner-urgent-care-6', '1592187760', 'http://www.taitjointreplacement.com', None, 'https://www.weecarelv.com', None, 'http://www.pizzanova.com', None, None, 'http://www.entebellamedical.com', 'http://www.deansgreenhouse.com', 'http://www.jazz.fm', 'https://locations.churchs.com/az-phoenix-7235', 'http://www.hashhouseagogo.com/', 'https://www.wyndhamhotels.com/hotel/15081?tel=18008899735&iata=00093785&cid=fe:hj:20170523:yl:pp:hjus:15081', 'http://www.hawaiianbarbecue.com', None, 'http://www.pizzahut.ca/', None, None, 'http://www.hawaiipoke.ca', None, 'http://www.bogdananghelmd.com', 'http://www.thegreenhousetavern.com', 'http://www.farmgirlsfood.com', 'http://www.museums.nevadaculture.org/nsmlv-home', 'http://www.graysbooks.com', None, 'https://www.clubpilates.com/fortmill', 'http://www.swc', 'http://www.4feldco.com/locations/madison/', 'https://www.simon.com/mall/arizona-mills/stores/disney-store-outlet-the', None, 'http://www.raymillphotography.com', 'http://www.thomasyu.ca', None, 'http://www.animalinnlv.com', None, None, 'http://www.ajlawplc.com', 'http://www.metrobark.com', 'https://www.get-go.com/', None, 'http://www.clevelandairport.com', None, 'http://jbamotors.com', '1592187838', 'http://www.wagonthedanforth.com/', None, 'http://www.toryburch.com', 'https://samurairamen-sushi.com', None, 'http://pizza.dominos.ca/Mississauga-Ontario-10348', 'http://www.universalscreenarts.com', None, None, None, 'http://www.keybank.com', None, 'https://cannacabana.com', '1592187864', 'http://www.sweetpeas.ca', 'http://cornercafewi.com/', 'http://www.restaurantbellissimo.com/fr', 'http://pigtailsandcrewcuts.com/charlotte-cotswold', None, 'http://www.calldanielhull.com?cmpid=F27M_BLM_0006', 'http://www.sidestreetpubandgrill.com/', None, 'http://www.DesertFitnessAZ.com', 'http://www.beardedchefaz.com', 'http://www.WickedBakery.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.gumbyspizzamadison.com/', None, None, 'http://www.makeafoodiecall.com', 'http://www.dunkindonuts.com', None, 'https://www.shadowmountaindentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.biennails.com', 'https://www.americasbest.com/store-list/avon-oh-44011/', 'http://www.wynnlasvegas.com/#Shopping/blacksatin', None, None, 'http://farmersagent.com/gelfond', None, 'http://cherryblossompools.com', 'http://www.eatnpark.com', None, 'http://www.activekidspediatrics.com', 'https://daisybluesummit.business.site', 'http://www.cedarcenterhardware.com/', 'http://www.hectorsmovingservices.com', 'http://locations.maurices.com/nv/lasvegas/clothing-stores-lasvegas-nv-1751.html', None, None, 'http://www.sonoramesquitegrill.com', 'http://www.airbornetrampoline.ca/locations/woodbridge/', 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'https://arizonaorganix.org', 'http://www.coinlesslaundry.com/23rd.html', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://littlerascalslearningcenter.com', 'http://www.barreljunction.com/location', None, None, '1592187957', None, None, 'http://www.kensingtonmakeupacademy.com', 'https://www.greulichs.com', None, 'http://www.eastwinddentallv.com', None, 'http://www.metroparktune.com', 'https://locations.theupsstore.com/az/gilbert/70-s-val-vista-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.trinitycathedral.com', 'http://kokosmiles.com', None, 'http://www.millerswaterdamageandrestoration.com/henderson-nv.html', None, 'http://ltgrill.com/', 'https://eastvalley.bintheredumpthatusa.com', 'http://www.swgas.com', 'http://www.FletcherHeightsAH.com', None, 'http://www.mooredalesailing.com', 'http://www.disgraceland.ca/', 'http://www.michaelkors.com/stores/united-states/nv/las-vegas/michael-kors-palazzo', None, 'https://www.kurevapes.com', 'http://www.sossystems.com', None, None, 'https://stores.petco.com/nc/gastonia/pet-supplies-gastonia-nc-1586.html', None, 'http://www.Azbiltmorebarbershop.com', 'https://www.zaxbys.com/locations/nc/concord/7781-gateway-ln-nw/', '1592228118', 'http://eyelovebeautybar.com/', 'http://www.justrolldup.com', 'http://www.7-eleven.com/?yelp=22886', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___estrella', None, 'https://www.gostorageone.com/self-storage/nv/las-vegas/maryland-pkwy/', 'http://www.cineplex.com/Theatre/cineplex-odeon-ajax', None, None, None, 'https://www.zimbrickhonda.com', 'https://locations.jackinthebox.com/us/ca/glendale/1200-w-glenoaks-blvd', 'http://www.kgautoworkspgh.com', 'https://www.americafirst.com/about/branches/branch-details.cfm?siteNo=104', 'http://www.goldenwestmanagement.com/', None, None, 'http://www.adega9.com', 'http://www.freshandwild.ca', 'http://www.scottsdalerestaurants.co', None, 'http://headtotoeinc.com', 'https://theeggworks.com', 'http://www.aqualunch.ca', 'http://www.steakonastone.us', 'http://www.thesavannah.com', None, None, 'http://www.ktnv.com/', None, 'https://honeycombsaloncollective.com', None, 'http://sunwest-az.com', 'http://www.rustikrotisserie.com', 'http://www.eliesfamilyrestaurant.com', 'https://www.lennar.com/New-Homes/Nevada/Las-Vegas/Las-Vegas/Mountains-Edge/Monterey-Ranch-The-Gardens/INHC', 'https://playgroundsdartzone.com', 'https://stores.peoplesjewellers.com/on/markham/5000-highway.html?cid=YEXT', 'http://www.tuttisantibynina.com', 'http://www.redsealnotary.com', 'http://www.cheekychicbb.com/', None, None, None, 'http://www.garciabailbonds.company', 'http://www.el-chameleon.com', 'http://www.miamistarglo.com', 'http://www.felinefabulous.com/', 'http://firebyjames.com', 'http://www.lumiermedicalspa.com', 'https://www.thaithaispaandmassage.com', 'http://www.lisaeleyphotography.com', 'https://corebodypilatesaz.com/locations/north-gilbert-pilates-studio', 'https://stores.thenorthface.com/NV/LAS-VEGAS/USA314/', 'http://local.firestonecompleteautocare.com/ohio/rocky-river/21210-center-ridge-rd/?lw_cmp=IYP_YPC_MLP_2089', 'https://leancanteengcu.wixsite.com/healthy', 'http://www.hargta.com', 'http://www.vanish-ink.com', 'http://www.elsombrerovegas.com/', 'http://www.SkatelandMesa.Com', 'http://www.aiellospizza.com', 'https://www.tristastevensonstylist.com', 'http://www.marisolcu.org/', 'http://www.theforumbarpar.com', 'http://www.usps.com/', None, 'https://www.carcolv.com', 'http://www.blacks.ca', 'http://barredefinitions.com', None, 'https://nailsatthelakes.business.site/?m=true', None, 'http://www.menschssecurityfilms.com', 'https://hovdeproperties.com', 'http://www.carolinasmedicalcenter.org/body.cfm?id=14', None, 'http://www.dentproaz.com', 'http://www.littlebangkokthairestaurant.com', 'http://thegallerysouthend.com/', 'http://www.desertsandsrvresort.com', None, None, 'http://www.townofyork.com', None, None, 'http://www.onedaytours.com', None, 'http://www.abercrombie.com', None, None, 'http://www.elpolloloco.com/locations/store/3859', 'https://dripedgeroofing.com', '1592228355', '1592228358', 'http://www.sleepnumber.com/?utm_source=Yelp&utm_medium=CPC&utm_term=CTA&utm_campaign=9f4Lf6iyxkIXfQw-hozi2w&cm_mmc=Yelp-_-Yelp-_-WebsiteLink-_-9f4Lf6iyxkIXfQw-hozi2w-904825&tag=904825', None, 'http://www.fairviewmall.ca/EN/Directory/Stores/Pages/NormaReed_1084A.aspx', None, None, None, '1592228370', 'http://www.qualityhomeinspectionspittsburgh.com/', 'https://mattressbyappointment.com/locations/nv/lasvegas/', 'http://retinanevada.com/', '1592228381', 'https://drcooperortho.com', None, 'http://www.brookcreekapartments.com', None, 'https://www.chevronwithtechron.com', 'http://www.citi.com', '1592228400', None, 'http://www.hobobillstrainhousellc.com', 'http://www.maidstr.com', 'http://www.teavana.com', 'http://www.webuycars.com/location', 'http://drphonerx.com', 'http://www.jaquelineandrea.com', 'http://sc-clinic.com/clinic/bay_and_college/', 'http://www.quailhollowresort.com/page/dining', None, None, 'http://www.chtools.ca', 'http://www.silvercollectionatthepark.com/?utm_knock=y', None, 'http://www.nvcoin.com', None, 'http://www.petco.com', None, 'https://www.giggles.ca/fr', 'https://www.associatedbank.com/location/WI/madison/2001-londonderry-dr', None, 'http://www.cascadeautogroup.com', 'https://eatcopperbranch.com', 'http://www.ZahlerProperties.com', 'http://www.somethinscooking.com', 'https://www.levinfurniture.com/furniture-store/oh/mayfield-hts/6051-mayfield-rd', '1592228466', None, 'http://www.bvinsurance.ca', None, 'http://www.csn.edu/library', 'http://www.waxon.ca', 'https://www.davidsbridal.com/?utm_source=Yelp&utm_medium=OrganicSearch&utm_term=84&utm_content=DisplayURL&utm_campaign=WebsiteListing', 'http://affyspremiumgrillscarborough.com', 'http://www.asapcity.com', '1592228491', 'http://www.libertymutual.com/insurance-office-madison-wi', 'https://www.ihop.com/en/restaurants-south-las-vegas-nv/7490-s-las-vegas-blvd-3096', None, None, 'www.ripspub.com', 'https://melodys-chair.business.site/#gallery', 'https://www.upack.com', '1592228513', 'http://www.customcoaches.ca', 'http://www.midabui.com', 'http://www.bostonsgourmet.com/', 'https://www.arrowheaddentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.saberhealth.com', None, 'http://www.trainersclubaz.com', 'http://acdentalvegas.com', 'http://www.crateandbarrel.ca/Stores/Store.aspx?storeid=201', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://impactptaz.com/scottsdale/', 'http://choicehotels.com/Suburban', None, '1592228544', 'http://www.plasticmaninc.com', 'http://www.mnmshop.com', None, 'http://www.desertstorage.com/scottsdale-az-storage-units', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', None, 'http://www.clubmonaco.ca', 'https://parkwoodslaundry.com', None, None, '1592228568', None, 'http://venushomesaz.com', None, None, '1592228579', 'http://fabulousfloorscleveland.com', 'http://www.clorebeauty.com/', 'http://bluediamondbestbitedental.com', 'http://www.wildeeasttownehonda.com', None, None, 'http://www.bootmaster.com', 'http://www.freevegasclubpasses.com/yelp', 'http://www.planetfitness.com/gyms/glendale-downtown-az-1110?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://booyah-inc.com', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', '1592228604', 'https://www.autonationbuickgmcwestsahara.com', None, 'http://www.highlandparkclubapartments.com', 'http://www.russellaquatics.com', 'http://www.eatatbobsdiner.com', 'http://www.huffsautomotive.com', '1592228619', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, 'http://www.freds-flowers.com', 'http://www.handandstone.ca/locations/jarvis-adelaide', 'https://www.azmobiletanning.com', None, 'https://www.audinorthlake.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, 'http://www.bunkhousekids.com/', 'http://www.flooringamericaofchandler.com/', 'http://bestbridalandtuxedo.com/', 'http://mcghies.com', None, 'http://www.lhsstudio.com', 'http://summerlinsmiles.com', 'http://alfornopizza.com/', 'http://www.thebatteryguy.com', 'http://www.piola.it', 'http://www.thaihousecalgary.com', None, 'https://agents.allstate.com/rosalie-gonzalez-las-vegas-nv1.html', 'https://www.champssports.com', 'http://www.greenlifecafemadison.com', None, None, None, 'http://www.napolipizzasqhill.com/', 'http://www.amptover.com', 'http://www.bronzecafe.com', 'http://www.envisionnv.com', None, 'http://www.conspirephoenix.com', 'http://findlayhonda.com', 'http://www.LendingPathway.com', None, None, 'https://www.walmart.com/store/2768/mesa-az/details', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://islingtongolfclub.com', None, 'http://HealthySkinLasVegas.com', 'http://cherryst.ca/', 'http://www.popsexotics.com', 'http://StrawberryPropertyManagement.com', 'https://www.extraspace.com/storage/facilities/us/pennsylvania/west_mifflin/1000000568/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, 'http://floresdecoloresart.com', 'http://www.chicos.com/store/home.jsp?cmp=MOC_yelp', None, None, 'http://www.cbdamericanshamanlv.com', None, 'http://www.sheacoco.ca', 'http://dollarcanada.ca', 'http://www.sapphirerealtyaz.com', 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://greenwithenvyaz.com', None, None, 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'https://www.redlobster.ca/locations/list/on/toronto/20-dundas-street-west', 'http://lemodernjapanese.com', 'http://www.edwardsmovinglabor.com', 'http://www.deforestfamilyrestaurant.com/', 'http://www.stusmotorcycletowing.com', 'http://www.foxpeterson.com', 'http://luckyspizza67.com', 'http://www.catboardingcharlotte.com/', None, 'https://familybraces.ca', 'http://www.letsdodinneronline.com', None, None, 'http://allstarhairnailslasvegas.com', 'http://www.coldstonecreamery.com/stores/22323', None, 'http://www.straightedgewallpapering.ca/default.htm', 'http://www.tsalonmesa.com', 'https://spiceclub.foodticket.ca/foodticket/cgi/bestel.cgi', None, 'http://mardaloopwellness.com', 'http://www.vegasCapital.com', 'http://7eleven.ca/store-locator/33259', None, 'http://shaggychic.com', 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', 'http://www.abbott-trophies.com/', 'http://www.aspca.org', 'http://archibaldmicrobrasserie.ca/index.php/fr/restaurant-blainville.html', 'http://cpm-apts.com', None, None, 'http://poshnailscharlotte.com', 'http://www.sallybeauty.com/', 'https://www.4wheelparts.com/stores/ohio/4wp-cleveland-oh-51', 'http://www.davesducts.com', None, None, 'http://www.trianglerealty.us', 'http://www.findlaychevy.com/', 'http://mountainpie.com', 'http://www.Districtlending.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.redmangousa.com', 'http://wtfexp.com', 'http://www.mi5tentertainment.com', None, 'https://www.bmoharris.com', 'http://www.ymcacharlotte.org', None, 'http://sphinx-cafe.com/', '1592228860', 'http://subway.com/', None, 'https://stoneandvine.com', 'http://www.papajohns.com', None, 'http://www.deltaco.com', 'http://illinishop.com', 'http://www.canadiantire.ca/en/store-details/on/warden-eglinton-on.store.html', 'http://medifastarizona.com', 'http://www.amorino.com', 'http://pdmtailor.com', '1592228887', 'https://www.casamiascottsdale.com', None, 'http://www.paragonphysicaltherapy.com', 'http://www.newviewrealtygroup.com', None, 'http://charlotteorthodontists.com/', 'http://www.clarkcountycourts.us/', 'http://www.redspaceevents.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.steaknshake.com/locations/23413-steak-n-shake-kenyon-road-urbana', 'https://www.cresthavengolf.ca', '1592228921', 'https://locations.wendys.com/united-states/ga/brunswick/164-altama-connector', 'https://www.palladiumeventcenter.com', None, 'http://www.royalganesha.com', 'http://mlk-smog-check.business.site', 'http://www.wemovewi.com', None, None, 'http://www.stevensplumbingac.com', 'http://akronfitnessandwellness.com/', None, 'https://www.wellsfargo.com', 'http://www.portofcleveland.com/environment-infrastructure/cleveland-lakefront-nature-preserve/', 'https://ad.doubleclick.net/ddm/clk/434046915;236895156;q', None, 'http://tiltedkilt.com/richmond-hill/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.investarrealestate.com/agent?xid=040101-01&name=Jacqueline-Kenoun', 'http://www.mirage.com/casino/race-and-sports-book.aspx', None, 'http://www.lilacbakeryaz.com', 'http://www.vegasvalleyphotography.com', 'http://desertmesapainting.com', 'https://www.chick-fil-a.com/arboretum', None, 'http://www.usmenuguide.com/honmachi.htm', 'http://www.cox.com', 'http://www.sgi-usa-lasvegas.org/', 'http://www.pancho-and-leftys.com', 'http://www.shell.com/', 'http://www.lofthairlounge.ca', 'https://www.metro.ca/trouver-une-epicerie/44', None, None, 'http://www.vfwpost3513.com', None, 'https://lasvegasurology.com', 'http://www.animalhousevetqueencreek.com', 'http://www.CLTvictor.com', None, None, 'https://www.shearexcellence.com/dilworth/', None, 'https://www.choicehotels.com/CN803?mc=blypypaf', 'https://thejoyfullkitchen.com', 'http://www.dbksalon.com', 'http://qdoba.com', None, 'http://www.francescasfaceliftoflasvegas.com', None, None, 'https://local.safeway.com/safeway/az/gilbert/90-s-val-vista-dr.html', None, None, 'http://massagemaniaglendale.com', 'http://www.chivino.com', None, 'http://www.integritytransportationpgh.com', None, 'http://www.dynastybuffetnc.com', 'http://www.dvf.com/', 'http://www.casitassanmarcos.com', 'https://sincitymoto.com', 'http://www.bodyandsoultherapy.ca', None, 'http://www.grapevinecabinets.com', 'http://www.arizonadanceartistry.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___metro_ii', 'http://www.nps.gov/jaga/', None, 'http://www.foothillsautoglassphoenix.com', 'http://www.iloveichibanaz.com', None, None, None, 'http://lahainagrillLV.com', 'http://www.adcopaint.com', None, 'http://everydaycafepgh.com', '1592229087', 'https://desertcastlepc.com', 'http://www.stonecreekroofingaz.com', None, None, 'http://www.bfshomewarranty.com', 'http://thomashinds.ca', 'http://www.dermatiquemd.com', 'http://www.bathemp.ca', 'https://nice-garden-landscape.business.site', 'http://www.browart23.com/location.html', None, 'http://www.millerframe.com', 'http://www.JimmyJohns.com', 'http://www.fabriziovegas.com', 'http://chensnoodlehouse.business.site', None, None, 'http://www.ridersinn.com', 'http://www.radjewellery.com', 'https://www.statefarm.com/agent/us/az/phoenix/eric-jackson-x4xfz21d000?cmpid=r6sy_blm_0006', 'http://yelp.com/elite', 'http://www.itsabaotime.ca', 'http://www.azchoicechiro.com', 'http://www.apple.com', '1592229145', 'http://www.superstarcarwashaz.com', 'http://futuredirectionsspa.com', 'http://www.heatherkphotography.net', 'http://www.cvcheart.com/scottsdale-princess-office/', 'http://jfkfinancial.com', 'http://www.canadiantire.ca', None, None, None, '1592229167', 'http://www.samuraicomics.com', None, 'https://nationwidevision.com/location/las-vegas-vision-center-silverado-ranch', '1592229176', None, 'https://ad.doubleclick.net/ddm/clk/435408715;237471434;h?https://www.hrblock.com/block-advisors/local-tax-offices/arizona/gilbert/67-s-higley-rd/2404?otppartnerid=9308&campaignid=pw_mcm_9308_9763', 'http://www.menchies.com', 'https://www.getpreloved.com', 'http://www.thainaka.ca/', 'http://retail.monroehardware.com/', 'http://cualv.com', 'http://www.starbucks.com', 'https://www.pteglv.com/locations/sean-patricks/deer-springs-5th-st/', 'http://www.mooseandbeargrill.com', 'http://assortedtablewine.com', '1592229204', 'https://www.haircutmenblakeneycharlottenc.com', 'https://www.basculebrewpub.com', 'https://www.aramarkuniform.com/our-locations/aramark-uniform-services-phoenix2', None, 'http://myloannailslasvegas.com', 'https://www.walmart.com/store/1093/rantoul-il/whats-new', None, None, None, None, 'http://www.mrsub.ca', 'https://www.metropcs.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.francisandsonscarwash.com/category/7889/francis-and-sons-car-wash-of-peoria-az.htm', 'http://www.swisschalet.com', None, 'http://www.nail-pretty.com', 'http://www.southernhighlandscyclery.com', None, 'http://www.wpxi.com', 'http://docromeopark.tk', 'http://guitartreemusic.com', None, 'http://www.dennysallnighter.com/', 'http://www.queencityclosets.com/', 'http://onestopnutrition.com', 'https://www.flavours-ajax.com', None, None, 'https://heightspestcontrol.com', 'http://vsnails.com', 'http://www.desertflowerseniorliving.com', 'http://www.reclaimedart.org', 'http://www.drdonnawoo.com/', 'https://www.sunsetgrill.ca', 'http://cuttingedgebarbershoplv.com', 'http://www.lllreptile.com/', 'http://www.cencispizza.com/wexford', '1592229284', 'https://www.gowireless.com/stores/az/scottsdale/scottsdale-scottsdale-fiesta/', 'http://haneysfamilyjewelers.jewelershowcase.com', 'http://www.evpools.com', None, None, 'http://www.activatechiropracticclinic.com', 'http://glendale.mensvitalitycenter.com/', 'https://www.potterybarn.ca', 'http://www.learningexpress.com/store/robinson/', 'http://www.letzrolloffroad.com', 'http://quickresponseplumbing.ca', 'http://hamptoninn3.hilton.com/en/hotels/arizona/hampton-inn-and-suites-phoenix-goodyear-PHXGYHX/index.html?SEO_id=YELP-HP-PHXGYHX', None, None, 'http://www.districtflats.com', None, 'http://www.urbanashop.com', None, 'http://www.goodwill.org', 'http://lvfurnituredirect.com', 'http://locations.maggianos.com/us/ohio/beachwood/beachwood', 'http://www.mobil1mentor.com', 'https://cocofreshtea.ca', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Gilbert-AZ-85234/922024/', '1592229337', None, None, 'http://bk.com/', '1592229346', 'http://hkrealtygroup.com', 'https://www.sparkletts.com', None, 'http://isabelcleaning.blogspot.com/', None, None, 'https://www.jackentertainment.com/cleveland/', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://www.90degreesapartments.com', None, 'http://www.fourlakesfamilydental.com', None, 'https://www.choicehotels.com/north-carolina/matthews/sleep-inn-hotels/nc032/rates', None, 'https://valleywiderestoration.com', None, 'http://fitnesstogether.com/matthews?utm_source=Yelp%20Web&utm_medium=Yelp%20Web&utm_campaign=Yelp%20Web', 'https://www.albertsons.com/home.html', None, 'http://www.bk.com', 'https://www.videogameswap.ca', 'http://www.summitdentallv.com', 'http://pekingman.ca', 'http://ismiledentists.com', 'http://handymanphoenix.com', None, 'http://www.vocellipizza.com/pleasanthills_pa', 'https://stores.sportsmans.com/sportsmans-warehouse/us/az/avondale/10145-w-mcdowell-road', 'http://bennybbq.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://thepetclub.com', 'http://www.zuppasdeli.com/', 'http://bacusbroshotdogs.com', 'http://www.toysrus.com/family/index.jsp?categoryId=2255956&camp=MISC:yelp:store:page:tru:111910', 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1207', None, 'http://www.dominos.com/', 'http://www.mindfulmotionphysicaltherapy.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.centralonbroadway.com/', 'http://www.stashcharlotte.com', 'https://locations.sonicdrivein.com/sc/tegacay/3039-highway-160.html', 'http://www.jtblandscapers.com/', 'http://www.exxonmobilstations.com/1721617-tesoro-62540-las-vegas#_62540-mobil-las_vegas', 'http://www.newimagephotography.com', '1592229448', 'http://sweetvirginiawax.com/', None, 'http://www.perfectflooringpgh.com', 'http://www.macmediainc.com', 'https://alohanailsblakeney.com', 'http://www.rinaldisdeli.com', 'http://www.wizardworld.com/cleveland.html', 'http://www.restaurantcrescendo.com/', None, 'https://www.performancemuffler.net', None, 'http://royal10cigar.com/', 'http://ashavecomics.com', 'http://www.brdiamondsuite.com', 'http://www.laurasecord.ca', '1592229483', 'https://5thavedeliandgrill.com', '1592229487', 'https://www.simon.com/mall/south-hills-village', 'http://www.positivechanges.com', 'http://www.aeacarizona.com', 'http://ajiichibansushi.com/', 'https://www.clearchoice.com/locations/dental-implants-las-vegas/?trans_id=webdisyelp&utm_campaign=Yelp&utm_source=YelpListing&utm_medium=Listing', None, 'http://www.dunkindonuts.com', None, 'http://www.superpumper.com', '1592229508', 'https://www.stance.com/retail/stance-scottsdale', 'https://www.tombstonetactical.com', 'http://www.lebouquetfloristandgifts.com', 'http://www.azmagician.com', 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', 'http://www.monroevillechryslerjeep.com', 'http://www.familylifecenters.org', 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://365gymllc.com', 'https://milios.com', None, 'http://www.padellaonavenue.com', None, 'http://crurestaurant.ca', 'http://www.arizonapaintingcompany.com/', None, 'http://www.equityapartments.com/Arizona/Phoenix-apartments/Scottsdale/San-Marcos-apartments.aspx', '1592229547', 'http://www.calakmulaz.com', 'http://www.pamperedpoocheslasvegas.com', None, 'http://torontovintage.ca', 'http://www.preservationcleaning.ca', 'https://www.homedepot.com/l/West-Aurora/IL/Aurora/60506/1957?cm_mmc=seo-yelp&', None, None, 'http://www.glowbeautycharlotte.com', 'http://www.attorneyramsey.com', None, None, None, 'http://www.kjsdental.net', '1592229581', 'http://www.buchanans.ca', None, 'http://www.khaanakhazanaaz.com/', None, 'https://www.torrid.com/store-details?StoreID=3512', 'http://www.croatiarestaurant.ca/', 'http://kblossomshop.com', 'http://www.phoenixlosburritos.com', 'http://drorona.com/', None, None, 'https://www.signaturestyle.com/locations/wi/madison/cost-cutters-maple-grove-shopping-center-haircuts-16214.html', None, None, 'http://www.mountainpark.org', 'http://www.alamo.com/', 'http://sweettomatoes.com', 'https://nixrockstargarage.com', 'http://glownailbarhenderson.com', 'http://www.heartbreakersalon.ca', 'http://lahmajounsevan.com/', 'http://www.tapino.com', 'http://www.hotdogonastick.com', None, 'http://www.ScruffyToFluffyLV.com', 'http://www.sagamorehillsanimalhospital.com', '1592229642', None, 'https://www.wellsfargo.com', 'http://www.balzermotorworks.com', None, 'http://www.pdqstores.com/gmaps/Wisconsin/MadisonArea/131.html', 'http://www.meadows-chiro.com', 'http://www.levinfurniture.com/furniture-store/pa/pittsburgh/5846-forbes-ave', None, 'http://www.futurekiddie.com', None, None, None, None, 'http://www.starbucks.com', None, '1592229673', 'http://southpointcasino.com/landing?cid=ypsp', None, 'http://www.shigatsusushi.com', 'http://lasvegasballroomdancing.com', None, None, 'http://www.brakemasters.com', '1592229689', 'http://www.homehardware.ca/en/dealer-microsites/1582-7/contact-information.htm', None, None, None, 'http://www.ascentcle.church', 'https://www.5spice.ca', '1592229702', 'http://www.hairbymegananton.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.charlottepediatricclinic.org', 'http://mastcoffee.ca', 'http://strutbridalsalon.com/', 'https://doctors.bannerhealth.com/provider/Daniel+Arrhenius/776226', 'http://www.bk.com', None, 'http://www.ultralighting.ca', None, 'http://ak-chinpavilion.com', 'http://www.zara.com', 'http://amyhogan.ca', 'http://www.chilis.com/', 'http://www.rainstormcarwash.com', 'http://Moreheadtavern.com', 'http://www.camelbackwomenshealth.com', 'https://az.aaa.com/agent-office-locations/nv/las-vegas/aaa-west-lake-mead-branch', 'https://www.luvasub.com', 'http://www.citysmokeclt.com', None, 'http://www.nailparade.com', 'http://stores.sallybeauty.com/az/mesa/beauty-supply-mesa-az-3292.html', None, 'http://www.Jerksogood.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.accuratecargo.com', 'https://losprimosmeats.com', 'http://www.grottolounge.com', 'https://www.plazaexecutive.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=KL%20execsuite', None, 'http://matthewscarwash.com', 'http://www.bbqislands.net', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://zscreamandbean.com', 'http://www.waxmuseum.net/', 'https://www.dominos.com', None, 'http://www.mccleanerslasvegas.com', 'http://jcls.jazzercise.com/facility/carnegie-jazzercise-center', 'http://duclostoys.com', 'http://www.therightguyshvac.com', 'http://www.thegourmetcave.com', 'http://tremontfarmersmarket.com/', 'http://www.nemdelight.com', None, 'http://www.mohaveeyecenter.com', 'http://www.yumeisushi.ca', None, 'https://www.early-bird.ca', None, '1592229815', 'http://www.pbjpittsburgh.com', 'https://www.starbucks.ca', 'http://clickserve.dartsearch.net/link/click?lid=43700006435129272&ds_s_kwgid=58700000444951114&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.conditandassoc.com', None, 'http://www.immortalsinconline.com', 'http://www.butterchickenroti.com', 'http://www.kirklands.com', 'http://www.eatgarbanzoaz.com/', 'http://thevertigogames.com', 'http://www.stadtcafetoronto.com', 'https://locations.waxcenter.com/nc/charlotte/charlotte-arboretum-0169.html', None, 'http://www.privyskincare.com', 'https://www.koekkoekfood.com', 'http://www.burgundysrestaurant.com/', None, 'http://www.usagymaz.com', 'http://www.bodhitreeacupuncture.com', 'http://www.tendertouchmoving.com', 'https://thaiexpress.ca', 'http://www.tenniscabana.com', '1592229868', 'http://www.yogurt-land.com', None, 'http://drivenfix.com', 'http://www.rocknes.com/index.htm', None, 'http://www.econolodge.com/hotel-rock_hill-south_carolina-SC139?source=pmfyelp&pmf=yelp', 'http://www.petco.com', 'http://www.countryinns.com/scottsdaleaz', 'http://www.bigsurffun.com', 'https://studiocpb.mysalononline.com', None, 'http://www.acoresrotisseriechicken.com/', None, 'http://www.oglolas.com', 'https://www.idealimage.com/medspa-locations/pennsylvania/pittsburgh-area/pittsburghwexford', None, 'http://www.bojangles.com', 'http://www.5cinco5.com', 'https://www.indiapalace.ca', 'https://crownpublichouse.com', None, None, 'https://twomaidswexford.com', None, 'http://www.luxdesign.ca', 'https://www.arizonaanimalwellnesscenter.com', 'http://www.clarkcountynv.gov/Depts/parks/Pages/winchester-cultural-center.aspx', 'http://www.renewalbyandersen.com/window-company/720-phoenix-az.aspx/?utm_source=Yelp&utm_medium=localization&mm_campaign=B5863EAA37E0931E94FEB25E4DEEDB54&mm_replace=true&engName=social_Yelp', 'http://www.shopjustice.com', None, None, 'http://www.perfecttimingentertainment.com', 'http://www.bsyhairstudio.com', None, None, 'http://www.welcomepharmacy.ca', 'http://www.friendshipsuites.com/', None, 'https://locator.chase.com/az/cave-creek/28238-n-tatum-blvd', None, '1592229955', 'https://www.panerabread.com/en-us/home.html', '1592229959', 'http://www.crossfitfury.com', 'https://order.qdoba.com', 'http://infinitydentallv.com/', 'http://www.maintenance-pro.com', None, 'https://www.brennansmarket.com', 'http://jetspizza.com', 'http://www.onthegrill.us', 'http://www.myrivertowne.com', 'http://www.plapreschool.com', 'http://www.dpauljewelry.com', None, None, None, 'http://www.forgoodnesscakesaz.com', '1592229997', None, None, 'https://www.eyeglassworld.com/store-list/las-vegas-(s)-nv-89121/', None, 'http://www.swansofinglewood.ca', 'https://www.aqualineplumberselectriciansacrepairphoenixaz.com', 'https://www1.shoppersdrugmart.ca', 'http://www.elirelocation.com', None, None, 'http://www.premiumsweets.ca', 'https://earls.ca/locations/calgary-tin-palace', 'http://www.beadworldinc.com', None, 'http://www.eastsidecannery.com', None, None, 'http://www.pooranivilaas.ca', 'https://www.navyfederal.org/branches-atms/locations/usa/az/phoenix/cmb/', 'http://www.landainails.com', 'https://www.accountingprincipals.com/locations/mesa-az-accounting-staffing-agencies', 'http://tendershawarma.ca', 'http://www.cherryaz.com', 'http://www.theindiegathering.com', None, 'http://www.prontomexicanfood.com', 'http://www.greatclips.com/', 'http://lasvegasrealestatetoday.com', 'http://www.terribleherbst.com/', 'http://freshdelicious.net/', 'http://www.selfconnection.ca', 'https://dealer.sprint.com/experts-choice', 'http://greatlakesbakingcompany.org', None, 'http://www.threedogbakerylkn.com', 'http://www.kiedrowskibakery.com/', None, 'http://www.boernercompany.com', 'https://www.ihop.com/en/restaurants-streetsboro-oh/9700-state-route-14-3606', '1592230084', 'http://pavelsjewelry.com/', 'http://www.suspectvideo.ca', 'http://www.tomasos.com', 'http://www.orenisbetter.com', 'http://az-ent.com', None, None, None, 'http://www.thespottedcouch.com', None, 'https://giorgio.ca/fr/restaurants/succursale/laval/', None, 'http://chiropractorpeoriaaz.com', None, 'http://www.gandgmarine.com', 'http://www.azdot.gov/mvd/', 'http://reeis.com', None, 'http://www.cuffsclothing.com', 'http://www.candomoving.com', 'http://www.cappysonwalnut.com', None, None, 'http://baraongles.ca', 'http://www.ellenmerkinod.com/', 'http://www.lynnbuss.com?cmpid=lvji_blm_0006', 'https://www.unitypoint.org/madison/home-health.aspx', None, None, 'https://www.ditkasrestaurants.com/Locations/Wexford', 'http://embassysuites3.hilton.com/en/hotels/pennsylvania/embassy-suites-by-hilton-pittsburgh-international-airport-PITATES/index.html', '1592230150', 'http://greenvalley.schoolofrock.com/?labelSource=Yelp&utm_campaign=yelp&utm_source=yelp&utm_medium=yelp&utm_content=yelp', None, 'http://www.lamexicana.ca', 'http://www.mymexquite.com', None, None, 'http://www.bayti.ca', None, 'http://www.rhythmcatsshow.com', None, 'http://bcpoolsupply.com', 'http://www.besolasvegas.com/', 'http://www.allclimatenc.com', 'https://www.wellsfargo.com/locator/bank/32__CATAWBA__ST_BELMONT_NC_28012/', 'http://www.innzonerainbow.com', 'http://www.airparkbike.com/', 'http://www.tolmtaz.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3825+Monticello+Boulevard-Cleveland+Heights-OH-44121/storeid=3337?cid=ps_ylp_2020', 'http://www.breathinghands.com', 'http://www.tropicalsmoothiecafe.com', 'http://phoenixnap.com/', 'http://www.canadel.ca', None, 'http://www.rogerkdowney.com/?cmpid=rkr3_blm_0006', 'http://www.caldensebakery.ca/', None, 'http://www.cegdealers.com', 'http://www.toysrus.ca', None, None, None, None, None, 'http://www.lvprestigecleaning.com', None, 'http://www.chtoyota.com', 'https://www.petersendean.com/?utm_source=yelp&utm_medium=referral', 'https://locations.waxcenter.com/pa/mccandless/mccandless-0287.html', 'http://www.turcopersian.com', 'http://www.haji-baba-tempe.com/Haji-Baba.com', None, None, 'http://www.jojosmenu.com', 'http://www.proficientclean.com', None, 'https://www.popeyes.com/store-locator/store/restaurant_82776', 'https://www.mattressfirm.com', 'http://www.snohc.com', 'http://www.napaautopro.com/auto-repair/alberta/calgary-renfrew-auto-service/', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://www.ezpawn.com/locations/nv/henderson/10075-eastern', None, 'http://www.ultimatecrc.com', 'http://www.camelbackcab.com/', 'https://www.duluthtrading.com/locations/?city=Belleville&StoreID=004&street-address=1107RiverSt.', 'http://www.chandlersmiles.com', '1592230275', 'https://www.forever21.com', None, None, None, 'http://www.nextcare.com/locations/az/98th/?utm_sourceYelp&utm_mediumLocal&utm_campaign98th', None, None, 'https://www.mattressfirm.com', 'http://www.gianteagle.com', None, 'http://www.boltonpizzapanini.ca', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2foh%2fakron%2fcopley-east&sisearchengine=1524&siproduct=2557_Bus', None, 'http://www.thanglong.ca', 'http://azfamilydentistry.com', 'http://www.deltaco.com', 'http://www.awakennutrition.com', 'http://www.alphasdiscoveryclub.com/indoorplayground', '1592230318', 'http://www.flourandbarley.com', None, 'http://www.nevadacareerinstitute.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/az/fountain-hills-5029.html?mcid=iyp:8368400', 'http://sonedental.com', 'http://www.get-go.com/storelocator/storedetails.aspx?storeid=294', None, 'https://www.goodyearautoservice.com/en-US/shop/AZ/Goodyear/000908232-85338-1430', None, 'http://www.atlasespressobar.com', 'http://www.foothillsrehab.com/', None, 'http://www.aliveandfreehypnosis.com', None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, 'http://floorshop.ca', None, 'http://www.southcharlotteanimalhospital.com', None, 'http://www.morfurniture.com', 'http://www.royalpgh.com', 'http://navarautoandtire.com', 'https://www.jerseymikes.com/8009', '1592230379', 'https://www.hilton.com/en/hotels/clehtht-home2-suites-cleveland-beachwood/?SEO_id=YELP-HT-CLEHTHT', 'http://www.kay.com', '1592230386', 'https://www.davidcreechmd.com', 'http://www.rabbatphoto.com', 'http://eddysautoservice.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZOT', 'http://www.estrestaurant.ca', 'https://www.180automotive.com', 'http://www.proaquatic.ca/', 'http://www.fastbiryani.com', None, 'http://asairoofing.com', 'http://www.lightrx.com/arrowhead', None, 'http://demetres.com', 'http://www.cre8iveevents.com/', 'https://www.4patientcare.ws/wsv3pro/web/webschedulerv3.aspx?SessionID=2050212', 'https://www.bcautospecialists.com/index.php', 'http://www.JimmyJohns.com', 'http://www.stonetheatres.com/#/sun-valley-14/4579599036', 'https://canyonstateac.com', 'http://www.inexcreativefloors.com', 'http://www.hotelvalleyho.com/vh-spa', None, 'http://www.rhodesranchgolf.com', 'https://www.isluxury.com', 'http://www.yogastyles.com', 'https://pho-oc-vietnamese-restaurant.business.site', None, None, 'http://www.arrowheadoralsurgery.com', '1592230459', 'http://www.fnfcarpetcleaning.com', None, None, 'http://www.slashsalon.com/', 'https://www.mgmresorts.com/en/hotels/united-states/mgm-northfield-park.html', 'http://musa-restaurant.business.site', '1592230477', 'http://www.wellsfargo.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://gourmetgringos.com', 'http://www.enlivant.com/communities/arizona/kingswood-place-surprise/?utm_campaign=local&utm_medium=Y&utm_source=listings', 'http://www.tiltedkilt.com/', 'http://www.azskindoc.com', 'https://www.tranquilwatersmedspa.com', 'http://www.KulturaToronto.com', None, 'http://www.kristinachartier.com', '1592230508', 'https://www.theprosperitygoddess.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLTCG', 'http://www.walmart.ca/en/walmart-meadowvale-supercentre/3054', 'http://www.harlemglobetrotters.com/', 'http://www.affordableappliancerepair.net', 'http://phoenixchildrens.org?utm_medium=local-listing&utm_source=chatmeter', None, None, 'http://www.avenuetaphouse.com', 'http://www.torrid.com', 'https://whiteoakanimalsafehaven.com', None, 'http://www.campusdish.com/en-US/CSW/UNLV', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.boomerangpilates.ca', 'http://www.lvsubzero.net', 'http://genghisgrill.com', 'http://www.pinkhouseboutique.com', 'http://www.sdmattress.com', 'http://www.prairiewindsvet.ca', None, None, None, None, 'https://www.pteglv.com/locations/pts-gold/st-rose-eastern/', None, 'http://theloftmedspa.healthcare', None, 'http://gottabegarys.com', None, 'http://www.thebiddlelawfirm.com', None, '1592230586', None, 'http://www.cookiesbygeorge.com', None, 'http://aquinolawgroup.com', 'http://skinnywimpmoving.com', 'http://locations.whichwich.com/AZ/Tempe/Tempe-Gateway', 'http://clevelandfurniturebank.org', 'http://thedizzy.ca/', 'http://www.libertyclinic.com', 'http://www.windowtreatmentslasvegasnv.com', None, 'http://www.portofsubs.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.familydollar.com', 'https://visionsource-studio-2020.com', 'https://locations.traderjoes.com/az/tempe/93/', None, 'https://www.galleryhiart.com', 'http://dyslexiacenter.com', 'http://www.latinmasstimes.com/Nevada/446', None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=891&utm_content=bpas', 'http://pipscafe.com', None, None, 'http://www.royaloakdentalcalgary.com', 'https://www.choicehotels.com/arizona/tempe/comfort-inn-hotels/az498/rates', None, None, None, None, 'http://www.aquasealwaterproofing.com', 'http://www.lovinghut.ca', 'http://www.rhinoexterior.com', 'http://store.concept1.ca/store/', 'http://havenhg.com', 'http://WorldsTallestChiropractor.com/', 'http://www.leahs.ca', 'http://thevaporsocial.com/', 'http://www.drpalluck.com', 'http://www.sunsetstation.com/dining/hooters/?utm_source=YELP&utm_medium=SOCIAL&utm_term=SS&utm_content=SS-PROPERTIES&utm_campaign=SS-YELP', 'http://www.newsonganthem.org', 'http://www.rosynails.ca', 'http://www.touchofthai.info', '1592230681', 'http://www.statebicycle.com', 'https://www.bodynbrain.com/scottsdale', 'http://greatscience.com/explore/exhibits/william-g-mather-steamship', 'http://www.arizonacharliesdecatur.com/', 'http://www.trainerjo.ca', 'http://www.myhenrybrown.com/?cs:pro=repman&cs:e=yelp', None, None, 'http://www.g1tour.com', None, 'https://urgentvet.com', 'https://www.mgmgrand.com/en/entertainment/grand-garden-arena.html', 'http://www.blimegreen.com', None, 'http://www.murgatroid.to', 'https://www.segwayofscottsdale.com', 'http://www.iandjfountainrestaurantaz.com', '1592230719', None, None, 'http://www.renegadecoffeeaz.com', None, 'http://www.earnhardtcjd.com', None, 'https://www.target.com/sl/north-olmsted/2016', 'http://schnitzelhub.com/', None, 'http://terramassagepgh.com', 'http://madjackspub.com/', None, None, '1592230745', 'https://www.mountainshadows.com', 'http://www.dukesupperdeck.com', None, 'http://www.qdoba.com/', None, 'https://nevadaeyephysicians.com/Henderson-Office', 'https://www.lebos.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.jetblue.com', 'http://doughboyspizzaandwings.com/', 'http://www.gordon-law-offices.com', 'http://www.callahans-flooring.com', 'https://madison.floorcoveringsinternational.com', None, None, 'http://www.festivalofcolorsusa.com/festival-of-colors/festival-colors-las-vegas-nv/', 'http://www.gigglingtomatoes.com', 'https://www.dominos.com', 'https://jose-cansecos-showtime-car-wash.business.site', 'http://lvpaiutesmokeshop.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FMSNME', 'https://wholehealthphoenix.com', 'http://www.salondecheveux.com', 'https://www.sportchek.ca/stores/hillcrest-mall.html', 'http://www.thebrooklineplumber.com', 'http://www.arcadiafarmscafe.com', None, None, 'http://lasvegashears.com/audiologist-las-vegas/', 'http://carlitosmokes.com', None, None, 'http://www.mypittsburghlocksmith.com/', 'http://goodwillsp.org/shop/retail-stores/weddington-road', None, 'http://www.magiclaserandaesthetics.com/', None, 'https://www.nextdoorwinebar.ca', 'http://store-locator.barnesandnoble.com/store/2212', None, 'http://www.fallasstores.com', None, None, 'http://www.coopercoons.com', 'http://www.aatexlawn.com', 'https://zacharylawgroup.com', 'https://local.executivecoin.com', 'http://www.azrealsolutions.com', 'http://www.thunderbirdim.com', 'https://www.insynco.com', 'http://www.drstevensabatino.com', None, 'http://www.lasvegasdogtrainers.com/', 'http://progressivedentalandortho.com/', 'https://www.chapmanhyundaiphoenix.com', None, None, 'http://www.a-natural-u.com', 'https://www.redstarvapor.com/stores/vape-shop-gilbert/', 'http://www.hcpnv.com', 'http://www.twtdbooks.com', 'https://www.stylistics.net', None, 'http://www.ashandkris.com', None, 'http://Www.SerenityRichmond.com', None, None, 'http://www.patrickssigns.com', 'http://www.havanacafe-az.com/', 'http://www.mogheltandoori.com', 'http://alpremium.ca/', 'http://www.wincofoods.com', None, None, None, None, None, 'http://www.mygreentreeapts.com', 'http://www.bearcreekaz.com', None, 'https://fixautousa.com/las-vegas-craig', 'http://www.inmotionstores.com', 'http://www.cadencecoffee.com', None, None, 'https://randrpaintingaz.com', 'http://www.labcorp.com', 'http://www.sunautoservice.com/auto-repair/nv/henderson', None, 'http://www.dubinwellness.com', None, 'https://www.alamo.com/en_US/car-rental/locations/location-details/US/PITT71-pittsburgh-international-airport.html?iataNumber=AL022237&affiliateRes=Y&cm_mmc=Yelp-_-IYP-_-National-_-null', 'http://www.pitaland.ca', 'http://www.tuttigelati.com/', 'http://www.burroburrito.com', None, 'http://terravitavet.com/', None, 'https://www.wingilariver.com/index.php/vq-vee-quiva-hotel-casino/dining/fatburger', 'http://imperialexcavatingaz.com', None, 'http://www.bartholomewphotography.com', 'http://lucillemadison.com', None, None, None, 'http://www.starbucks.com/store/9334/', 'http://www.decoraport.ca/francais/', 'http://www.johnnyrockets.com', 'http://boucherville.delfriscos.ca', 'http://beerbatter.ca', 'http://www.quiznos.ca', None, None, None, 'http://withoutwalls.tv/', 'http://Www.kristinlloy.com', 'http://www.letswrap.biz', 'http://www.truevalue.com/hometruevalue', 'http://www.allmetalsrecyclingllc.com', None, 'http://www.jumprestaurant.com/', None, None, 'http://www.chandlercustomcycles.com', None, 'http://www.bwh-services.com', None, 'https://locations.dignityhealth.org/oasis-hospital-phoenix-az', None, 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'https://locations.panerabread.com/oh/bainbridge-township/8480-east-washington-street.html', None, 'http://www.fred-vincentvw.com/', 'http://www.audreyjanellebeauty.com', None, 'http://www.lauraleesalon.com', 'https://www.bartlett.com/locations/Phoenix-AZ.cfm/?yelp_ads_lop%C3%8A', 'http://appliance-repair-pittsburgh.pa-biz.com', None, 'http://www.starbucks.ca', 'https://sandees-water-n-ice.business.site', None, 'http://www.orvis.com/cleveland', 'http://www.acehardware.com/store-details/06234', 'http://www.fantasticsams.com', None, 'https://www.availvapor.com/north-olmsted', 'http://www.georgiossalonspa.com/', 'http://www.sexyplusclothing.com', '1592231074', None, 'http://eatmegourmetcatering.com', 'http://www.onceuponachildstow.com/', None, None, 'http://www.pianotuneraz.com', 'http://www.framersworkshop.net', None, 'http://www.sunglasshut.com/us/?cvosrc=display.yelp.LasVegas', None, '1592231097', None, None, 'https://www.mandalaybay.com/en/nightlife/rhythm-riffs.html', 'https://www.walmart.com/store/4356/las-vegas-nv/details', 'http://www.bosmeadery.com/', 'https://www.steaknshake.com', None, 'http://www.dolcelucano.com/', None, 'http://storelocator.pepboys.com/pepboys/stores/phoenix/cactus/00747', 'http://www.jumparoundpartyjumpers.com', 'http://www.NextLevelTreeLLC.com', None, 'http://www.jimmyscoffee.ca', 'http://www.bigotires.com/regions/Nevada', None, 'http://www.onegooddoctor.com', 'https://www.aqualityelectric.com', 'http://www.actionappliancepitt.com', 'http://www.fetishfalls.com', None, 'https://www.camdenliving.com/scottsdale-az-apartments/camden-foothills?cm_mmc=Yelp', None, 'http://www.themilkshakefactory.com', 'http://www.opalasvegas.com/', None, 'http://relaxologywellness.com', 'http://www.greatclips.com/', 'http://l.macys.com/biltmore-fashion-park-in-phoenix-az?cm_mmc=Yelp_Stores-_-Phoenix-_-n-_-451&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Phoenix_451&m_ac=yelp_stores&m_ag=n', None, None, 'http://hmshost.com', 'http://www.pagoda.com', None, 'http://www.2fixmyair.com', 'http://lazioitalianbakery.com/', 'https://www.flyfrontier.com', 'http://warraichmeats.com/', 'http://bhelwalaindianfood.com/', 'https://www.enterprise.com/en/car-rental/locations/us/nv/north-las-vegas-craig-rd-5404.html?mcid=iyp:8368400', None, None, None, 'https://azvent.com/locations/estrella.php', None, None, 'http://www.ahealershand.com/', None, 'http://www.thedelevagroup.com', '1592231200', None, None, 'http://www.libertywildlife.org/', None, None, 'https://www.emilianos.net', None, 'http://www.klassynailscalgary.com', 'https://stores.cortfurnitureoutlet.com/arizona/chandler/150-south-kyrene-suite-1/?utm_source=yelp&utm_medium=organic&utm_campaign=localmaps', 'http://www.pintoranch.com', None, 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'http://www.institutefordriverssafety.org/', None, 'http://allautobattery2007.com', 'http://www.paulstailors.com/', None, None, 'http://www.purplesagesalon.com', 'http://www.rockwoodnaturalmedicine.com/', None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'https://www.westelm.com', 'http://robertostacoshop.com', None, 'http://www.banfield.com/veterinarians/nc/charlotte/bky?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89015/601-in-henderson/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-601&utm_content=website-link&howheard=IYE', 'http://banditolv.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://www.bigotires.com/regions/Nevada', 'https://www.appletreedentalforkids.com', 'http://www.lizzynco.com', 'http://www.skylarparkeraz.com', None, 'http://www.btvape.com', 'http://www.tenrestaurantaz.com', 'http://www.zoestrunk.com', None, 'https://www.popalock.com', 'http://www.zaborfh.com', 'https://www.sunamg.com', None, 'https://www.awomanschoiceinc.com', 'https://www.walmart.com/store/2720/madison-ms/whats-new', 'http://www.cannonschophouse.com', 'http://www.school-for-massage.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216494&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.aquariuslandscapinglasvegas.net', None, 'http://www.snowdentistry.com', None, 'http://www.westhillsnissan.com', 'http://www.marcos.com/', 'http://bermanchiro.net', None, 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?STORE=629&language=EN', 'http://www.myazsmile.com', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', None, '1592231336', None, None, 'http://agentpestcontrol.com', 'http://www.gilleyslasvegas.com', 'http://www.drsmarkantone.com', 'http://www.dollarama.com', 'http://www.vbsconstruction.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'http://www.rockruninn.com', 'http://www.jamburritos.com', 'http://www.icenowaz.com', 'http://www.thebarrelinn.com', 'http://www.pierdeorleans.com', None, 'http://www.transitionsquad.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.hennashoppe.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'http://www.buffalophoto.net', 'http://www.skyzone.com/ca/mississauga', 'https://www.destinationhotels.com/tempe-mission-palms/dining/tempe-restaurants', 'http://www.summitfamilydentist.com', 'http://www.notoriousautodesigns.com', 'https://www.wellsfargo.com', 'http://www.walmart.com/', '1592231397', 'https://centralusa.salvationarmy.org/danecounty', 'http://www.thetheodore.beer', 'http://www.michaelruffattodmd.com', 'http://www.quiktrip.com', 'http://www.metropolis-living.com/', 'http://www.buildabear.com?sc_cid=ds:yelp:profile', None, '1592231415', 'http://lagourmandinebakery.com', 'https://www.artclassesforkids.com', None, 'https://www.coulternissan.com', 'http://www.harborfreight.com', 'http://www.loveandcaresitters.com/', 'http://scottsdaleprinting.org', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.wallacefloral.com', 'http://kellyclark.com', 'http://www.papa-luigi.com', None, 'https://www.wellsfargo.com', 'https://nativegrillandwings.com/location/pebble-creek/?utm_source=Yelp&utm_medium=Local&utm_campaign=Pebble_Creek', 'http://www.skinnydippingpools.com', 'http://www.kfc.com', '1592231454', 'https://eyetique.com/squirrel-hill', None, None, 'http://www.bargainballoons.ca', 'http://www.sonicdrivein.com/', 'https://www.erbertandgerberts.com/locations/?store_address=53703', 'http://www.papagnos.com', None, 'http://www.johnnymcguires.com/vegas/', 'http://www.beaumontalignment.com', None, 'https://www.dapperandstout.com', 'http://www.uhhospitals.org/north-olmsted/urgent-care', 'https://www.barnettfalls.com', None, 'http://www.greatdanepub.com/', 'http://www.skodagordon.com', 'http://www.raffmobilemechanic.com', '1592231495', None, 'http://www.maac.com/south-carolina/columbia/the-fairways?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', None, 'http://www.dannburg.com', None, None, None, 'http://routes.ca', 'https://locations.tiaa.org/nc/charlotte/8500-andrew-carnegie-blvd?tc_mcid=bn_yelplocal_0618', 'http://sweetpeacafe.moonfruit.com/', 'http://www.EveryKidsDentist.com/?sc_cid=Yelp_Listing', 'http://www.healthyplanetcanada.com/stores/index/view/store/13', None, 'https://squarefeat.com', 'http://www.advancedtherapeutics.ca', 'http://www.eighteeneight.com/beachwood-oh', '1592231531', 'https://www.moes.com/find-a-moes/pennsylvania/wexford/100189?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', None, 'http://www.arizonabestmaids.com', None, 'http://www.amournailsandspa.com', None, None, 'https://www.hilton.com/en/hotels/phxgthx-hampton-suites-phoenix-gilbert/?SEO_id=YELP-HP-PHXGTHX', 'https://www.cooperfamilydentistryaz.com', None, 'http://www.hendersonchevrolet.com', 'http://www.dentalassistingaz.com', 'http://www.senecacollege.ca', None, 'http://philthyphillys.com', 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', 'https://www.restoration1ofgreaterlasvegas.com', None, 'http://www.arizonalasik.com/', 'http://www.downtownhomeinn.com', 'https://stores.petco.com/pa/pittsburgh/pet-supplies-pittsburgh-pa-1812.html', 'https://www.saigeboutiquesalon.com', 'https://barbaraannsalterations.com', 'http://www.vivitaspa.com', None, 'http://footreflexologychandlergilbertaz.com/', 'http://www.rycoplumbing.com', 'https://www.petpeoplestores.com/strongsville-store.html', 'http://www.paulsacehardware.com', None, '1592231602', 'http://www.thegrubclub.com/a/daddydukes', 'http://mesaunderground.com/', 'https://refinedlightingaz.com', 'http://www.thechildbirtheducator.com', None, None, None, None, 'http://www.desertstorage.com/scottsdale-az-storage-units', None, 'http://www.petiterestaurant.ca', None, None, '1592231633', 'http://www.falcononeclt.com', 'http://www.fracascleveland.com/', 'https://stores.arhaus.com/oh/akron/2246-west-market-street.html', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'https://www.lolplay.ca', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=101', 'http://www.somethingnewmedia.com', 'http://www.mughaircuts.com/', 'http://www.pcmloan.com', None, None, 'http://sanfrancescos.com', 'https://www.thephoenician.com/phoenician-tavern/', 'http://www.aeopowersports.com', 'https://www.redlobster.com/locations/list/az/peoria/7921-west-bell-rd', 'http://locations.arbys.com/us/nv/north-las-vegas/1465-w-craig-rd.html', None, 'http://www.usps.com/', 'https://az.aaa.com/agent-office-locations/az/phoenix/aaa-paradise-valley-auto-repair', None, 'http://www.ellamentssalon.com', 'https://shuyi.ca', 'http://www.macxn.com/stores/madison-wisconsin', 'http://pedispanailbar.com', 'http://www.vaudreuilvolkswagen.com', 'https://www.anytimefitness.com/gyms/2160/Scottsdale-AZ-85266/?utm_source=yelp&utm_medium=local', 'http://www.mcdonalds.com', 'http://www.patriotmovers.us', 'http://www.furnitureappliancemart.com/current/Stores/Madison_West_Wisconsin_Furniture_Store.aspx', '1592231701', 'http://www.yorkvilleespressobar.com', None, 'http://www.italianvillagepizza.com/', None, None, None, 'http://www.rossstores.com', None, 'http://www.honeycombedhair.com', None, None, 'http://frostyvalleygolf.com/', 'http://www.builderzwarehouse.com', 'https://www.callawayirrigation.com', 'http://www.Boothbuilt.com', 'https://www.lalasercenter.com/centennial/?utm_source=yelp&utm_medium=centennial&utm_campaign=centennial%20dermatology%20and%20laser%20cancer', None, None, 'https://www.idealimage.com/medspa-locations/nevada/las-vegas-nv-area/lasvegassummerlin', 'http://www.epoxyfloorsphx.com', None, 'http://www.bmdprinting.com', 'http://www.warfieldhairbar.com', 'http://www.jandsautoservice.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'http://Ljhaircuts.com', 'https://www.caesars.com/flamingo-las-vegas?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=FlamingoLasVegas&utm_content=hotel', 'http://www.bitsandbytesllc.com', 'http://www.timhortons.com/', 'https://stores.dickssportinggoods.com/nv/las-vegas/1266/', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', 'https://www.zerorezmadison.com', 'http://www.sheppardvillagedental.com', None, 'http://www.avenue.com', '1592231786', None, '1592231790', 'https://www.camdenliving.com/tempe-az-apartments/camden-tempe', None, 'http://www.qdoba.com/', None, None, 'http://www.pizzahut.ca/', 'http://www.cafelabella.com/', None, 'http://www.agassiprep.net', 'http://www.scarlettplus.com', 'https://gilberteast.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.planetfitness.com/gyms/madison-west-broadway-wi-797?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://lisnoodles.com', 'http://idealcustomflooring.net', '1592231823', 'http://www.picanhalv.com', None, None, 'http://elpalenqueeastlake.com', None, None, 'http://universitycoinandjewelry.com', 'http://www.rajskitchennc.com', 'http://www.strongsvilleheating.com', None, 'http://www.thebutcherspantry.com', 'https://locations.dignityhealth.org/emergency-room-at-arizona-general-hospital-glendale', 'http://www.artisticalloys.com/', 'http://www.silkmedspa.ca/', 'http://www.arizonalodgingexperts.com/owner-support/scottsdale-az-property-management/', 'http://allntattoo.com', 'http://www.belleetboeuf.com', 'http://www.spice9cuisine.com', 'http://lensfactory.ca', 'http://www.mark-taylor.com/arizona/stone-oaks/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.aldoshoes.com/ca/en', 'http://www.shopartmart.com', 'http://www.womeninneed.net/', 'https://www.atozdiscountdepot.com', 'http://lifetimegaragedoorsaz.com', 'https://www.alphaandomegadogtraining.com', 'http://ajustbrewcoffee.org', 'https://www.brooklynbedding.com/showrooms/arizona/phoenix-buckeye/?utm_source=yelp.com&utm_medium=referral&utm_campaign=yelppage', 'http://www.yellowjersey.org/', None, None, 'http://www.cafelouise.ca', None, None, 'http://www.izzazu.com', 'http://www.posterjack.ca', 'https://local.firestonecompleteautocare.com/nevada/las-vegas/3770-s-maryland-parkway/', 'http://orangeleafyogurt.com/frozen-yogurt-store/OH/gates-mills-/6679-wilson-mills-rd?id=384', 'http://www.zaidmoving.com', 'http://www.exoticnailstouch.com/', 'http://www.cartelbrewery.com', 'http://www.greasemonkeyhuntersville958.com', 'http://dresslersrestaurant.com', 'http://superdupermovers.ca', 'http://aquasportscuba.com', 'http://mortlandpt.com/', 'http://www.firstimpressionnails.ca', 'http://www.coffeepubs.ca', 'http://www.empirebagels.com/', None, None, 'http://www.mcramyun.com', 'http://www.ledesmafootandankle.com', 'https://www.bobevans.com/our-restaurants/locations/146?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'https://www.papillon.com/las-vegas-tours/?utm_source=yelp&utm_medium=cpc&utm_campaign=papillon-las-vegas', 'http://www.bytesbackdatarecovery.com', 'https://www.macu.com/Branch-Locations/AZ/Mesa/Mesa-Branch/0033', None, None, None, None, 'https://www.regmovies.com/theatres/regal-manor-twin/1841?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Manor+Twin', None, 'http://www.barneys.com/location#!/stores/14', 'http://www.getenergysmarter.org', 'http://hooterscasinohotel.com', None, None, None, None, 'http://www.dianasseafood.com', 'http://www.theloadeddog.ca/', 'https://www.restaurantszibo.com/les-restos/boisbriand', 'https://www.prolinkprotection.com', None, 'http://www.hairhappiness.com', None, 'https://www.playfalcongolf.com', 'http://www.cpracademylv.com', 'http://www.quiktrip.com', 'http://www.kennelcarevet.com', None, 'http://www.athletico.com/locations/urbana/', 'https://www.sgtclean.com', 'http://brucehalllaw.com', 'http://www.westernskiesgolf.com/', 'http://homewoodsuites3.hilton.com/en/hotels/ontario/homewood-suites-by-hilton-toronto-mississauga-YTOHWHW/index.html?SEO_id=YELP-HW-YTOHWHW', None, 'https://www.medicentres.com/chiropractic/', None, '1592232037', 'http://home.vivoli.ca/', 'http://www.ncdentist.com', None, 'http://www.poetryjazzcafe.com/', 'https://locations.tropicalsmoothiecafe.com/nv/henderson/10612-south-eastern-avenue', 'http://www.malleys.com', None, 'http://www.junk-works.ca/locations/toronto-north', None, None, 'https://www.frontieraptmovers.com', 'https://www.hattendo.ca', None, 'http://www.housecallnotary.ca', 'http://bunsofsteelbootcamp.com/', '1592232072', None, 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=118&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-118', 'http://thekeyrealtyteamaz.com', 'http://www.arcadiachiro.com', None, 'https://www.180smoke.ca/vape-shop-etobicoke-islington-electronic-cigarettes', None, 'http://www.soulpepper.ca/', None, 'http://www.autotruckandfleetservices.com', 'http://hiltongardeninn3.hilton.com/en/hotels/north-carolina/hilton-garden-inn-charlotte-concord-CLTCOGI/index.html?SEO_id=YELP-GI-CLTCOGI', 'http://igniteperformance.net', 'http://www.smartbookingtravel.com/', None, 'http://www.sashandbustle.com/', 'http://www.bestratemtg.com', 'http://hibachisan.com/', None, None, 'http://www.acneadvisors.com', None, None, 'https://www.classictan.biz', 'http://www.cityofhenderson.com/henderson-happenings/parks-and-trails/locations-and-features/reunion-trails-park-and-amargosa-trailhead', 'http://juicdlife.com', '1592232129', 'http://www.tutortime.com/your-local-school/phoenix-az-6086/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://www.letstalktherapy.com', 'http://www.downtownerlv.com', 'http://www.melrosekitchenaz.com', 'http://www.somethinsweet.ca', None, None, 'http://www.climateprollc.com/', 'http://Www.artistichandsmassage.com', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', 'http://www.scottsdaleeyesurgerycenter.com', 'https://www.brewerairporttoyota.com', 'http://springfieldgolfresort.com/', None, 'http://www.bodyworkscentral.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.elpasobarbeque.com/', None, 'http://www.mitchiesmunchies.com', 'http://www.jardinalex.com/?srccode=yelp_track', 'http://www.homesmartinternational.com', 'https://mkbjj.com', 'http://www.outside-inspirations.com', 'http://www.mayereyecarelv.com', 'https://kimmynailsandspa.weebly.com', 'http://www.tree-removal-phoenix.com', None, None, 'http://www.e-mg.com', 'http://www.amayaexpress.com/', None, 'http://www.winners.ca', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FLASGR', '1592232211', 'https://www.loblaws.ca/store-locator/Glen+Erin+Drive%2C+Mississauga/1011?storeId=1011', 'http://www.tamalerialaurita.com', None, '1592232222', None, 'http://www.CharlotteHealthCenter.com', 'http://www.ihg.com/intercontinental/hotels/gb/en/cleveland/clehb/hoteldetail', 'http://www.rockymountaintails.ca', None, 'http://www.meineke.com', 'http://www.semprepizzapasta.com', 'http://symposiumcafe.com/woodbridgerestaurants.html', None, 'https://elementsmassage.com/Phoenix-Arcadia', 'https://graylinelasvegas.com', '1592232247', None, None, 'http://iwearthebest.com', 'http://www.repeteslv.com', 'http://www.managestaff.com', None, 'http://www.urbanpalm.com', 'http://www.livelifeblended.com', 'http://www.empire.edu/cosmetology-schools/north-carolina/charlotte-pineville', None, 'https://rightspacestorage.com/self-storage-locations/nevada/las-vegas-nv-storage-units/3043-N-Pecos-Rd/', None, 'http://www.phxortho.com', None, 'http://www.petvalu.com', 'http://hummusfactorylv.com', None, None, 'http://www.pelicanssnoballs.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4755+West+Ann+Road-North+Las+Vegas-NV-89031/storeid=2989?cid=ps_ylp_2020', 'http://nvpicapart.com', 'http://www.mrosmow.com/', 'http://www.lofgreens.com/', None, 'https://rtcatcafe.org', 'https://www.surpriserental.com', 'http://tjmaxx.tjx.com/store/stores/storeLocator.jsp?_requestid=62549', 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6006', 'http://www.btbouncies.com', 'http://www.tinnenfamilychiropractic.com', 'http://www.blushlane.com', 'http://archwaychandler.greatheartsacademies.org', None, None, 'http://www.grillies.ca', None, 'http://www.backcarechiropractic.com', 'https://www.mypetmarket.com', 'http://www.visionworks.com', None, None, 'https://www.anytimefitness.com/gyms/288/Las-Vegas-NV-89139/?utm_source=yelp&utm_medium=local', 'http://www.happyhauscleaning.com', None, 'http://www.steaknshake.com/locations/23949-steak-n-shake-cherry-road-rock-hill', 'http://www.irepex.com', 'http://glutenfreegoat.com', 'http://www.rossstores.com', 'http://www.dogdayslasvegas.com', None, 'https://www.allvalleycarcare.com', 'http://www.thepigeonguy.com', None, 'http://www.etchsalon.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.sugarfactory.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, 'http://quicksmiles.com', 'http://www.southbrookpumpkins.com', 'http://www.starbucks.com/store/9298/', None, 'http://www.fender.com', 'http://www.arizonaveterinaryoncology.com', None, 'http://chollafamilydentistry.com', 'http://www.aliveprintshop.com', 'http://www.skipro.com', 'https://www.cyclegear.com', 'http://sunriseautosaleslv.com', '1592232418', None, 'http://www.warmspringssurgicalcenter.com', None, 'http://www.safewaytire.net/locations/mode/22/4623-superior-avenue-cleveland-oh-44103.aspx', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=8248', None, 'http://radioshack.com', None, None, None, 'https://ad.doubleclick.net/ddm/clk/300150600;127077036;j', None, 'http://www.kinospainting.com/', 'http://www.themercurylounge.com', 'http://www.westcanadian.com', None, '1592232457', None, 'http://www.tequilaranchcleveland.com', 'https://www.peaceloveandlittledonuts.com/locations/hudson-oh', 'http://www.azsportscenter.com', 'http://www.UnitedBeautySupply.com', None, 'http://www.phoenixpubliclibrary.org/Locations/Pages/Cholla.aspx', None, 'http://www.chilinoodlecorner.com/', None, 'https://3scocoffeebar.com', 'http://leafandbloom.com', 'https://www.fastmed.com/urgent-care-centers/phoenix-az-walk-in-clinic-maryvale-parkway/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'https://www.homedepot.com/l/Cave-Creek/AZ/Phoenix/85022/480?cm_mmc=seo-yelp&', 'https://www.wyndhamhotels.com/hotel/30821?tel=18882935571&iata=00093785&cid=fe:bh:20161215:yl:pp:hawus:30821', 'http://mcithedoctorsoffice.ca/patients/37-clinic-Mt.-Pleasant', None, None, 'http://www.sabatinospizza.com', '1592232509', 'https://chatters.ca', None, None, 'http://www.greenvalleyrange.com', 'http://www.gangnamasianbbqdining.com', 'http://www.gemini-arcade-palace.com/', 'https://www.mcalistersdeli.com/locations/nc/cornelius/19930-west-catawba-avenue-suite-150-1067', 'http://www.ProOutdoorServices.com', 'http://www.winners.ca', 'http://la-dulce-espera.business.site', 'https://ad.doubleclick.net/ddm/clk/434331165;236814625;c', 'https://cortatefurniture.com', 'http://a519chocolate.com', 'http://gregstruckandautorepairil.com', None, 'http://www.visionsourcewestsahara.com', None, None, 'http://mobileglowaz.com/', 'http://donutparlor.com', 'http://www.greenvalleyobgyn-nv.com', 'http://www.awhitepondparadise.com', 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', None, 'http://latinoservices.net', 'https://www.xtendbarre.com/studio/charlotte', 'http://sharpedgebeer.com/index.php/locations/brasserie', 'http://www.cavopgh.com/', 'http://www.ymcaofpittsburgh.org/sampson/', 'http://www.planetfitness.com/gyms/las-vegas-flamingo-nv-611?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.lovesac.com/', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', None, 'http://thewingfactory.ca', 'https://lmp360media.com', 'http://locations.in-n-out.com/234', 'http://www.Learn2PlayNow.com/', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.JimmyJohns.com', 'http://www.lakeforestcc.org', 'http://www.brittwiththebrush.com', 'http://www.gentlemenscutlakewylie.com/', 'http://www.premierfoliage.com', 'http://www.playacabana.ca/', None, None, 'http://areyoukenilworthy.com/', 'https://www.interstatebatteries.com/locations/all-battery-center-peoria-il', 'https://www.homedepot.com/l/Arrowhead-Ranch/AZ/Glendale/85308/475?cm_mmc=seo-yelp&', None, 'http://www.scottclarknissan.com/?utm_source=yelp&utm_medium=business_url&utm_campaign=local-citations', None, 'http://www.goodlifefitness.com/locations/ontario/northyork/don-millseglinton?source=yelp-websitelink-northyorkdon-gl', 'http://fightertownpaintballpark.com/', '1592232641', 'http://www.barbecuedoctor.com', 'http://www.zinburgeraz.com/locations/gilbert', 'http://www.ifrrealestate.com', 'http://www.botanyflowers.ca', 'http://www.homedepot.com/l/Curity/ON/Toronto/M4B-3L8/7012', 'http://dimurasmoving.com', 'http://www.academyofballroomdance.com', 'https://www.redroof.com/extendedstay/hometownestudios/property/AZ/Phoenix/HTS1059', 'https://mhausnailbar.com', 'http://www.cataldi.ca', 'http://www.thenorvalpancakefactory.com', 'http://www.greenmontvet.com', 'http://realalbertamoving.com', 'https://www.hopewayfoundation.org', None, 'http://www.midas.com/phoenix/store.aspx?shopnum=1241&dmanum=684001', 'http://www.oomomostore.com', 'http://yuphas.com', 'http://lekensington.ca', 'http://us.christianlouboutin.com/ca_en/', 'https://www.redlobster.com/locations/list/il/champaign/1901-n-prospect-ave', None, None, 'http://www.calgaryexpo.com', 'http://www.cheesecakeetc.biz', None, 'http://www.cocktailemporium.com', 'http://west50.ca/', 'http://www.donvalleyendoscopy.com', None, 'https://www.interdent.com/gentle-dental/locations/az/peoria/14155-n-83rd-ave-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.chillinaz.com', 'https://www.oberweis.com/ice-cream-and-dairy-stores/Champaign', 'http://www.orthodoc.aaos.org', None, 'http://www.pregocalgary.com', 'https://www.canadiantire.ca/en/store-details/on/markham-on0.store.html', 'http://www.robstreeremoval.com', 'http://www.sodexousa.com/', 'http://www.tempestlukeshospital.com/', 'https://ikonick.com', '1592232742', 'http://www.yourvacationhome.ca', None, 'http://crockerparkwinefestival.com', 'http://svpsports.ca/stores/steeles', 'http://www.calgarycoop.com/stores/brentwood', 'http://www.papaceo.ca', 'http://www.bulkbarn.ca/en-ca/index.html', 'http://www.alphagraphics.com/centers/tempe-arizona-us004/index.html', 'http://www.floppypawspetsupplies.com', 'http://www.phxsecrets.com', 'http://www.apria.com', 'http://www.onceuponachildscottsdale.com/', 'https://www.belfor.com/en/us/belfor-usa-offices/nevada/las-vegas', None, 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://www.adept.fit', 'http://cibocalgary.com', None, 'http://www.thoseguysmotorcycle.com/', 'https://chadloveservices.com', 'http://phoenixtenniscenter.org', 'http://lagerheads.us', 'http://pizza22ribs.com', 'http://www.funnymagicforkids.com', 'http://barksidebistro.com', '1592232800', 'https://summithomesnv.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.frock.ca', 'http://www.myspace.com/rockyseastside', 'http://www.smgvegas.com', 'http://www.toronto.ca/parks/prd/facilities/complex/467/index.htm', 'http://www.monro.com', 'http://www.wildwingrestaurants.com/franchisees/angus-glen/', 'https://www.goodeyes.com/locations/phoenix/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-phoenix&utm_content=website', 'http://www.einsteinbros.com/', 'http://www.jiffylube.com', 'https://www.moonvalleynurseries.com/locations/northwest-las-vegas?utm_campaign=yelp&utm_source=yelp-nv&utm_medium=rancho', 'https://la-canasta.com', None, 'https://locations.panerabread.com/oh/sheffield-village/5382-abbe-rd.html', '1592232836', 'http://www.frizzhairexp.com', None, None, None, 'https://vespersalon.com', 'http://www.michaelhill.ca/on/demandware.store/Sites-MichaelHillCA-Site/en_CA/Stores-Details?StoreID=148', None, 'http://rudyspub.org', 'http://www.lavishmotoring.com', 'http://www.warehousegroup.ca/el-furniture-warehouse-queen-st', 'http://www.naillacquersalon.com/', 'https://www.benjaminfranklinplumbing.com/las-vegas/', 'https://stores.pepboys.com/nv/las-vegas/506-s-decatur-blvd.html', '1592232869', 'https://www.metropolish17.com', 'http://www.streetsofnewyork.com', None, 'http://www.thepostalroute.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://theritzoflasvegas.com/', 'http://www.greentreehealthandmassage.com', 'http://www.dmvnv.com/', None, None, None, 'http://www.hotelarts.ca', 'http://www.runnymedewalkinmedical.com/', None, None, None, 'http://www.vitalitytap.com', 'http://www.bk.com', None, 'http://sekaisushi.net', 'https://www.frysfood.com/storeHours?store=66000623', None, 'http://ptownbar.com/', 'http://www.limozarizona.com/', 'http://www.lakeshorewellness.ca', 'http://en.hestiatea.com', 'http://www.snapfitness.com/torontohighpark', None, 'http://www.yogapulsestudio.com', 'http://www.veraiconsalonspa.com', '1592232943', None, 'http://www.jaybuickgmc.com', None, 'https://www.menzieschryslerdealer.com', 'http://www.dickblick.com/stores/pennsylvania/pittsburgh/', 'http://www.handandstone.ca/locations/aurora', None, None, 'http://BluBurger.com', 'http://www.nurturedmama.com', 'http://www.cwtow.com', None, 'http://www.fitnesscafemenu.com/', None, 'http://www.vegasmartialarts.com', None, 'http://drtangeyecare.com', 'http://b2burgersbrews.com', 'http://www.copyrite.ca', None, None, 'http://wingardsalon.com/', 'https://hilalgrill.com', None, 'http://www.extremeenergypros.com', 'http://www.ciaobabycatering.com', 'https://baycity-movers.com', None, 'https://www.bannerhealth.com/locations/peoria/banner-urgent-care', None, 'https://www.associated-dental.com/practices/associated-dental-care-chandler', 'https://www.starbucks.ca/store-locator/store/1020633/177-holland-street-east-177-holland-street-east-bradford-on-l-3-z-1-x-8-ca', None, 'http://www.spencersonline.com', None, None, 'http://w.subway.com', 'http://myomedicalmd.com', None, 'http://www.karma.salon', None, None, 'http://powerautobrokers.com/', None, None, 'https://www.ihg.com/holidayinnexpress/hotels/us/en/las-vegas/lasqr/hoteldetail', 'http://robertostacoshop.com', None, 'http://www.allbrightsmile.com', None, 'http://www.publicenemytattoo.net', 'http://www.lucysseacove.com', None, None, 'https://www.nofrills.ca/store-locator/Mario+%26+Selina%27s+nofrills+%28Royal+York+Rd.%29/1371?storeId=1371', None, 'http://beersoftheburgh.com', None, 'http://dnister.ca', 'http://www.wilsonparkerhomes.com', 'http://www.priyashairsalon.com', 'http://www.patoisjamaicanrestaurant.com', 'http://www.thebeautyspotstore.com', 'https://opdaz.com', 'http://www.bearmountainsports.com', 'http://www.foresightchiropractic.com/', 'http://www.palominolv.com/', 'http://www.ralphlauren.com', 'https://wildfire.sclv.com/Barleys?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.lawrysonline.com/lawrys-primerib/las-vegas', None, None, '1592233109', 'http://www.chnv.org/OurCare/HealthyLivingInstitute.aspx', 'http://www.dunkindonuts.com', 'http://602massage.com', 'http://www.zaffron.ca/', 'http://www.bodyvision.com/arrowhead-studio/', None, 'http://www.hhgregg.com', None, 'https://cityofspice.com', None, 'https://varmintgone.com/locations/varmint-gone-matthews-north-carolina/', 'http://eastlakecanoe.com/', 'http://www.auroraarizona.com', 'http://www.papamurphys.com/', 'http://www.marcstreeservice.com', 'http://www.majesticpalmsapartments.com/', 'http://www.peoplesjewellers.com', None, 'http://www.tempe.gov/city-hall/community-services/community-recreation-centers/diablo-stadium', 'http://stonecreekfurniture.com', 'http://www.centralavenuedental.com', 'https://www.planetfitness.com/gyms/kent-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', '1592233167', 'https://www.atozlandscapinglv.com', None, 'http://www.sundevilauto.com/locations/az/chandler/chandler-22', 'http://www.wickeremporium.ca/', None, 'https://paulmitchell.edu/pittsburgh', 'https://www.chapters.indigo.ca/en-ca/home/storelocator/storeDetails/939', None, '1592233187', 'http://www.rainbowfeatherco.com', None, 'https://www.coca-colacoliseum.com', 'http://www.masterworksautomotive.com/', 'https://www.gianteagle.com/Stores/Store/?storeId=5831', 'https://www.goldfishswimschool.com/wexford/', 'http://www.elcampesinospgh.com', 'http://www.noforksgivenclt.com', None, 'http://www.gokartslasvegas.com', None, None, 'http://www.jacksonlimousines.com', 'http://www.thelashlounge.com/salons/waverly/', None, 'http://www.ACabLV.com', 'https://www.jumagallery.com', 'http://www.suncityawning.com', 'http://www.carrvalleycheese.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.ashleyfurniturehomestore.com/furniture-stores/united-states/nv/henderson/henderson?cmpid=2016YELP', None, 'http://ratewisemortgage.com', None, None, 'http://www.krispykreme.com', 'https://www.oyorooms.com/76426?utm_campaign=US_PHX004&utm_medium=listing&utm_source=yelp', 'http://www.comda.com/en_ca/', 'https://www.veinscarolina.com', 'http://wedosystems.com', 'https://stores.bestbuy.com/az/avondale/10035-w-mcdowell-rd-1109.html/?loc=ns100&ref=NS', '1592233263', 'http://safransmarket.com', 'http://www.kitchenbathroomremodeling.net', 'http://www.atengarofalodental.com', 'http://diamondnailsofmahomet.com', 'https://www.orangetheory.com/en-us/locations/arizona/surprise/16846-w-bell-rd-suite-106/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.pizzuvio.com', 'http://www.ayrsleynailbar.com', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://www.sushimaster.ca', 'http://silverstatelocksmith.com', 'https://svdpmadison.org/shop/verona/', None, 'http://www.totalsportsmedicine.com', 'http://www.brazascharlotte.com', 'http://www.nutrition-rush.com/stores.html', 'http://brazilianblowoutsbykatie.com', 'http://www.stammhouserestaurant.com/', 'http://www.eyetecheyes.com', None, 'http://www.girly-girlz.com', None, 'http://www.gatesmillsplace.com', 'https://www.flawlessbyhanna.com', None, 'http://www.sdpetresort.com', 'https://locations.togos.com/ll/US/AZ/Scottsdale/7369-N_-Via-Paseo-Del-Sur*-Ste_-104', 'https://www.aireserv.com/red-mountain', 'http://www.ampm.com', 'http://www.custommedicalmassage.com/pre-and-perinatal.html', 'http://www.nanakcarwash.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://masteldrycleaning.com/?utm_medium=CTA&utm_source=VYRLYelp', 'http://www.verizonwireless.com/stores/arizona/mesa/val-vista-204086/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.gotransit.com', 'http://www.geckoshadesolutions.com', 'https://www.blissnailspasc.com', 'https://locations.timhortons.com/ca/on/oakville/494-dundas-st-w.html', None, 'https://locations.massageenvy.com/pennsylvania/bethel-park/5223-library-road.html', 'http://blueiguanapools.com', 'http://www.heirloomsalon.net', None, 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'http://www.kingswayvanlines.com', 'http://www.todaysmenu.ca', 'http://lasvegasnora.com/home.html', None, 'http://www.maac.com/florida/orlando/retreat-at-lake-nona?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://www.7-eleven.com/?yelp=19726', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89015/601-in-henderson/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-601&utm_content=website-link&howheard=IYE', None, 'https://www.calgarycoop.com/stores/shawnessy/', 'http://www.lawroofing.net', 'http://www.palaisroyale.ca/', 'http://www.blackpeppergrill.com', '1592233399', 'http://www.copps.com', 'http://www.greeningenuity.ca', None, 'https://modellacewigsandhair.com', 'http://www.lebowitzdental.com/', 'http://JamesonAndStaggs.com', 'http://www.atlas-autobodyinc.com/', 'http://www.eyebrowsnatural.com/', 'https://www.miragegm.com', 'https://www.hilton.com/en/hotels/clttohx-hampton-suites-charlotte-ballantyne/?SEO_id=YELP-HP-CLTTOHX', None, 'http://www.designingwomanohio.com', None, 'http://www.southwestjudo.com', 'http://www.healingedgeaz.com', None, None, 'http://stores.fossil.com/az/scottsdale/scottsdale-fashion-square-8304', 'http://www.mrfallstree.com', None, None, None, None, None, None, 'https://www.hilton.com/en/hotels/pitsrhx-hampton-suites-pittsburgh-airport-south-settlers-ridge/?SEO_id=YELP-HP-PITSRHX', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sweetlanasbridal.com', 'http://www.nakedpizza.biz', None, None, 'http://www.generaltsoskitchen.com/', 'http://www.alteredimage.net', 'http://www.azclar.com', None, 'http://www.songlowboutique.com', '1592233480', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.excellenceindentistry.com', 'http://www.roofitright.com', 'http://www.3riverslocksmith.com/', 'https://locations.dollartree.com/il/champaign/546/', None, None, None, 'http://www.belllexusnorthscottsdale.com', 'http://www.osbornplace.com', None, 'http://tavernamericana.com/', 'http://www.paybackpest.com', 'http://www.donscigars.com/', 'http://parkinn.com/hotel-torontoca', 'https://www.carolinaasthma.com/location/eastover/', None, 'http://www.lickshomeburgers.com/', None, 'http://www.atsol.com', None, None, None, 'http://oxurban.com', 'http://salonliftohio.com/', 'https://www.cvs.com/minuteclinic/clinic-locator/nc/belmont/2233.html', None, 'http://www.dairyqueen.com', '1592233542', 'http://www.thecarolinadental.com', 'http://www.dentistryofarizona.com', 'http://goodearthcoffeehouse.com', 'http://www.newmarketinn.com/', 'http://www.gilbertperfectskin.com', 'http://www.dermimatch.com', 'https://joeyrestaurants.com/location/joey-crowfoot', 'http://www.health.gov.on.ca/en/public/programs/telehealth/', 'http://www.proarmament.com/index.html', '1592233565', 'http://www.bodricksbbq.com', None, 'http://www.yalebrothers.com', 'http://www.supremeshutters.ca', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://excel-pro-services.com', 'http://www.minpermanentmakeup.com', 'http://www.brainandspineaz.com', None, 'http://www.harmonyvet.com/', 'https://m.costco.com/warehouse-locations/summerlin-las-vegas-nv-685.html', None, 'http://SolisWaverly.com', None, 'http://www.ziggystavernpgh.com', 'http://mustangairmechanical.com', 'https://zestyclean.com', 'https://mvpmodernbarbers.com/bridgeland/', 'http://www.arizonahomeworks.com', None, 'http://www.perfectionistdetailing.com', None, 'http://www.mkt.com/desertrootskitchen', None, 'http://www.rotorooter.com', None, None, None, 'http://www.nafloans.com/', None, 'http://www.ztrip.com', None, 'http://www.umc.org', '1592233641', 'https://www.getgocafe.com/stores/pa/pittsburgh/baum-blvd-getgo/3064', '1592233647', None, '1592233652', 'http://onlyfaces.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=14314', 'http://www.erx247.com', 'http://www.marcos.com/', 'http://www.azextensionsbyjess.com', None, None, 'https://locations.dennys.com/OH/PARMA/247530', None, 'http://www.thaionyonge.com', None, 'http://www.pawstwoclaws.com', '1592233683', 'http://www.reliable.vegas', 'http://www.a1thevacuumshop.com/', 'http://www.zumiez.com', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.francisandsonscarwash.com', 'http://arizonapinatas.com', None, 'http://saachispa.com', None, 'http://www.papaprimoz.com', 'http://www.thevoodoolounge.ca/', None, None, 'http://www.themesshall.ca', 'http://goldstarsvc.com', None, 'http://www.neatfreakz@vpweb.com', 'http://www.cityofmadison.com/parks/find-a-park/park.cfm?id=1139', 'http://www.eggspectation.com', 'http://www.yamasushihouse.com', 'https://mylocalmcds.com/willow-pass-concord', 'http://www.tlcpedsaz.com/', None, 'http://www.lvthaimassage.com', 'http://www.frenchconnection.com', 'https://www.giascanvas.com', 'https://affordablebathroomsofaz.com', 'https://www.regmovies.com/theatres/regal-franklin-square/1845?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Franklin+Square', None, 'https://www.optumcare.com/state/specialty-care/specialist-locations/rose-parkway-oncology.html', 'http://levetto.com/', None, 'http://www.richlane.ca', 'http://www.pureandsimple.ca', 'http://www.moneyinminutesnv.com', 'http://www.MyMightyMoversAz.com', 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://nathansfamous.com', 'http://www.wvimaging.com/', 'http://www.motimahal.ca', 'http://4lifenaturalfoods.com', 'http://www.uptowncarservice.com', 'http://www.classicmobileairbrushtanning.com', None, 'https://www.walmart.com/store/1464/charlotte-nc/whats-new', 'http://www.medinaoh.org/Parks/Reagan_Park', 'http://westendfood.coop/farmers-market', 'http://www.larichs-pizza.com', None, 'http://aaapws.com', 'http://www.3Brewers.ca', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'http://blushcleveland.com', None, '1592233815', None, None, None, 'http://northcarolinafertility.com', 'http://www.lasvegascustomloans.com', 'http://www.tacomamaonline.com', None, 'http://www.jacksonswash.com', 'http://perfectpastryonline.com', 'http://www.clevelandexpress.net/index.html', 'http://www.azturfmasters.com', 'http://sidewalkcafeeuclid.com', 'http://mpmvegas.com', 'http://www.streetsofnewyork.com', 'https://www.thejoint.com/arizona/surprise/surprise-48024', 'http://www.playderecord.com', 'http://www.tranquil-bodyworks.massagetherapy.com', 'http://elsombrero.ca/', None, None, 'http://vipbestlasvegaselectrician.com', None, 'http://www.creativedds.com', None, 'http://www.apexendo.com', 'http://senortequilacantinagrill.com/', 'http://abloomsalon.com', 'http://marketcitycaffelasvegas.mypub.website', 'http://www.starbucks.com', 'http://www.quiznos.com/', 'http://www.mesaaz.gov/parksrec/Parks/MountainView.aspx', 'http://www.victoriasfamily.com', None, None, 'https://northtryonlaundromat.com', None, 'http://www.theastrologystore.com/', None, 'http://www.elomsbraiding.com', 'http://www.downtowntorontochiropractor.com', None, None, 'http://www.matthewsfarmersmarket.com/Index.html', 'https://www.wyndhamhotels.com/hotel/52963?tel=18666154223&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52963', 'http://www.secondlookbooks.org', 'http://www.firstqualityroof.com/', None, 'http://www.visionquestbooks.com', None, None, None, None, 'http://www.sallybeauty.com', 'https://www.bowlero.com/location/bowlero-christown?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'http://www.babysbadassburgers.com', 'http://www.phoenixelectricianstoday.com', 'http://www.saulterstreetbrewery.com', None, None, None, 'http://www.labcorp.com', 'https://www.giovannisonline.com', None, None, 'http://www.marbleslab.ca', 'https://www.lush.ca/on/demandware.store/Sites-LushCA-Site/en_CA/Stores-Info?StoreID=129', 'http://www.eatatovereasy.com', 'http://chirotrendz.com/', 'http://www.greenvalleyranchresort.com/dining/china-spice.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=GVR&utm_content=GVR-PROPERTIES&utm_campaign=GVR-YELP', 'http://www.directv.com', 'https://www.gymboreeclasses.com/en/locations/NC/Charlotte/?utm_campaign=Charlotte&utm_medium=website&utm_source=Yelp&utm_content=yelp+page', 'http://brosandbettys.com/', None, 'http://www.lemonfreshcleaning.com', 'http://jetaction.com/', None, None, 'http://www.getitfixed.me', 'http://primozzpizzeria.com', 'http://www.cascadenc.com', 'https://www.fantasticsams.com/about/regions/phoenix-az/fantastic-sams-mesa-az-4', 'http://www.isaute.ca', 'http://www.piesquared.com', 'http://www.thewhitenailsspa.com', 'http://www.bestmassagecenter.com', None, '1592234018', None, 'https://www.brakemasters.com/new-site/stores/1901-n-scottsdale-rd-scottsdale-az/', 'http://happyjoes.com', None, 'http://www.ArrowheadScoopers.com', 'http://www.neatmethod.com', None, 'https://www.usps.com/', 'http://hancockfabrics.com/', 'http://www.albertayogacollege.com', 'http://www.sterling2cleaners.com', 'http://www.royalyorkmeatmarket.com', None, None, None, 'http://signaturenorthwest.com/agent/andrew-lunsford/', 'http://www.madcatpets.com', 'http://www.chasin-tails.ca', 'http://www.roxannesdriedflowers.com', 'https://www.amco-autoglass.com', None, 'http://handymanserviceslasvegasnevada.com', 'http://www.arrowheadnails.com', 'http://www.mcsorleysrestolounge.com/', 'http://www.cityofhenderson.com/parks/parks/sonata_park.php', 'http://www.heartlandpethospital.com', 'http://www.cruisin7th.com', '1592234082', 'http://www.abbotthearingaidcenter.com', 'http://www.townetavernrestaurants.com', None, 'http://www.subvetclinic.net', 'https://stores.jcpenney.com/nv/lasvegas/clothing-stores-lasvegas-nv-2848.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2848', 'http://wendyandersonlaw.com', 'http://www.globalpetfoods.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://nailskathylinhdesign.com/', None, 'http://www.meadowslv.com', 'http://www.ccrfurniturecleaning.com', None, 'https://www.bostonmarket.com/location/university-heights-oh-483/', 'http://www.senecacollege.ca', 'https://www.walmart.ca/en/stores-near-me/markville-mall-supercentre-3053', '1592234121', 'https://www.munichmotorco.com/service-your-car', None, 'http://www.guardianautoglassphoenix.com', 'http://www.thetacobros.com', 'https://www.popeyes.com', 'http://www.impactps.com/', 'http://www.phoenixmentalist.com', 'https://cagiautoglass.com', None, None, 'https://periodontics-dentalimplants.com', 'http://www.nowandthenretro.com', None, None, None, '1592234160', 'http://www.lesportsac.com', 'https://lvsmilecenter.com', None, 'http://www.mysewingroom.ca', 'https://ad.doubleclick.net/ddm/clk/458685338;262921492;w', None, None, 'http://www.shawnessysouthvet.com/', 'http://www.jandbappliance.com', None, None, 'http://www.piscessushi.com', None, 'http://www.techniquerestaurant.com/', 'http://www.scubamagic.biz', None, None, None, None, None, 'https://www.blackmetalfirearms.com', 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', 'https://locator.chase.com/nv/henderson/637-n-stephanie-st?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.laalv.com', None, 'http://www.lasvegasswimacademy.com', 'https://www.target.com/sl/waterfront/1253', 'https://www.cloudcarpetonelasvegas.com/about-us/las-vegas', 'http://phoenixcenterforthearts.org/', 'http://www.phoenixknifehouse.com', None, 'http://www.calranch.com', 'http://honeydont.work', None, 'http://www.orobrewing.com', None, 'http://seefuhair.com', 'https://www.petsmart.com/stores/us/az/scottsdale-store0130.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.youngshawaiianstylekitchen.com', 'http://www.brickyardgrounds.ca/', 'http://www.donrandleslawoffice.com/', 'http://johnnyrockets.com', 'https://www.planchatoronto.ca', 'http://www.pawgo.co', None, 'https://www.hertz.com/rentacar/location/unitedstates/northcarolina/charlotte/CLTT12', 'http://www.mtnparkchiropractic.com/', 'http://aquatechplumbingaz.com', None, None, 'http://www.larrygjones.com', 'http://www.myguardianselfstorage.com', '1592234284', None, 'http://www.orleanscasino.com/entertain/bowling?disid=wmm_yelp_to_corporate_bowlingcenter_organiclink', 'http://www.starbucks.com/store/15154/', 'http://www.thefrenchbee.com', None, 'https://finercustomjewelry.com', 'http://colournailssalon.com/', 'http://yummymarket.com/', None, None, 'http://robertostacoshop.com', None, 'http://azpermanentcosmetics.com/', 'http://www.midas.com/toronto/store.aspx?shopnum=9259&dmanum=857001', 'http://www.ocotilloeyecare.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.amerisent.com', 'http://backwards.club', 'https://antikka.ca', 'http://www.turnstyleconsign.com/ahwatukee-phoenix.php', None, None, 'http://www.pjsdayspa.com', '1592234337', 'http://thebrowbomb.com', 'https://www.dunnedwards.com/directory/store-list/summerlin-078', 'http://drscottminer.com', 'https://www.peoriaford.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', None, 'https://www.crashofrhinospainting.com', 'https://www.kohls.com/stores/nv/lasvegas-668.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.thebakeryphx.com/', 'https://www.usps.com/', None, None, 'http://www.burlingtoncoatfactory.com', 'http://dalesbodyworksllc.com/', 'http://www.petworksco.com', None, 'http://yumyumsofcle.com', 'http://www.thedogdasher.com', 'http://www.hartshornstudios.com/', 'http://europeanpaverssouthwest.com/', None, 'http://www.maleesonmain.com/', 'http://www.equityresidential.com/', 'https://www.publicstorage.com/arizona/self-storage-gilbert-az/85233-self-storage/850?pid=wyelp&CID=1245&CHID=AFL', 'https://www.flavorsoflouisianacajun.com', 'http://www.madbatterbakers.com/', None, 'http://tempefarmersmarket.com/', 'http://www.8bitentertainment.com', 'http://machinodonuts.com', '1592234413', None, 'http://www.westmarine.com', 'https://www.nasm.org', None, None, None, 'https://locations.jackinthebox.com/us/nc/charlotte/7725-pineville-matthews-rd', None, 'https://locations.dennys.com/PA/NEW-KENSINGTON/249565', None, None, None, 'https://www.serviceheroesaz.com', 'http://zabblv.com', None, '1592234448', 'http://www.quiznos.com/', 'http://www.workhorsemarine.com', None, 'http://www.readytorolltire.com', 'https://www.beefjerkyoutlet.com', '1592234462', None, None, '1592234467', None, 'http://christophersfinedrycleaning.ca', None, None, 'http://www.donatos.com', 'http://menu6.org', 'https://www.charlottemeetings.com/charlotte-convention-center', 'http://www.lubestop.com/Locations/Wadsworth', 'http://www.papamurphys.com/', 'http://www.adidas.ca', 'http://www.arizonastoragecenters.com', 'http://www.excelauto.biz', 'http://www.edingersurgicaloptions.com', 'https://www.949atthedistrict.com', None, 'http://www.lvtattoo.com', 'http://www.hobbylobby.com/StoreLocator/Search?Latitude=43.1438143&Longitude=-89.35114950000002&SearchOn=+53704&SearchDistance=25', 'http://www.tacorrito.ca/', 'http://www.pintville.com', '1592234514', None, 'http://www.functionalaestheticdentistry.com', 'http://www.bsjplumbing.com', 'http://www.unitedmessengers.com', 'http://www.kelilabee.com', 'http://www.lovecloudvegas.com', 'http://www.vaco.com', 'http://www.aptfind.com', 'http://www.piesunlimited.com', None, 'http://www.vitalant.org', 'https://locations.usbank.com/index/arizona/tempe/east-elliot-rd-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', '1592234547', None, 'https://agents.allstate.com/the-bell-agency-henderson-nv.html', None, 'http://www.heroburgers.com', 'http://www.kidsrkidslasvegas.com', 'http://artistichair.studio', None, None, 'https://www.qualtire.com', None, None, '1592234573', 'http://www.animalsupplyhouserockhill.com/', 'http://www.muchoburrito.com', None, 'http://suitenectarsalons.com', 'https://www.filibertos.com', None, 'http://www.truwest.org', 'https://www.dipnailboutiqueocotillo.com', 'http://www.paradisedentalgroup.com', None, 'http://dreamydrawdental.com', 'http://www.mcmurray-manalodental.com', 'http://www.thompsonsautorepair.com', '1592234607', None, None, 'http://www.homewatchcaregivers.com/phoenix', 'http://www.tailgateclothing.com', 'http://www.buybuybaby.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.uwhealth.org/locations/detail.jsp?locationid=124', None, 'https://davidguyettphotography.smugmug.com', 'http://www.midge.ca', None, 'http://mkhouseconsulting.com', 'http://www.torontosculpturegarden.com', None, 'http://EventRents.net', None, 'http://usedcars12.com', 'http://www.azartrestoration.com', 'https://www.circlek.com/store-locator/us/peoria/9476-w-olive-ave/2706468', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://waxingaroundtown.com', 'http://www.xtremehomeservicesaz.com', 'http://lasmejorespupusas.weebly.com/', 'http://www.redendos.com', 'http://www.CrowdControlLV.com', 'https://www.kaltire.com/en/stores/locations/?source=yelp_track&StoreID=867', 'http://rickjohn.com', 'http://www.pplusic.com', 'http://www.jabzboxing.com/glendale', None, 'http://www.madisonautodetail.com', 'http://www.fourquet-fourchette.com', 'http://www.dazzlingrestaurant.com', 'http://montereyvetclinic.ca', 'http://www.mrbsfamoussale.com', 'http://www.carserviceoflasvegas.com', 'http://www.suntreehealingarts.com', None, 'http://cirqnightclub.com', 'http://www.ampm.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.zabas.com/', 'http://summerwindsnursery.com/az/home?utm_source=yelp&utm_medium=text_link&utm_campaign=website', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYCWA', 'http://www.santanfamilymedicine.com', 'https://www.circlek.com/store-locator/us/gilbert/888-s-higley-rd/2703373', None, 'https://canyoncreekrestaurant.ca/square-one/', 'http://www.artificialgrassinstallers.com', 'http://www.customcyclerescue.com', 'https://www.usstoragecenters.com/self-storage/nevada/las-vegas/us-storage-centers/135', 'http://www.inland-group.com/location/phoenix/', 'http://www.phxprep.com', 'http://www.DLCphoenix.com', 'http://www.babiesrus.com', 'http://www.ashtangayogalv.com', 'http://upmccancercenters.com/network/upmchillman.cfm', 'https://www.swimco.com/?utm_campaign=Market&utm_source=YELP', None, 'http://www.the-alley.ca', 'https://stores.advanceautoparts.com/pa/murrysville/4010-william-penn-highway?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', None, 'http://www.donalfonsotoronto.com', 'https://locations.jackinthebox.com/us/ca/glendale/1200-w-glenoaks-blvd', 'https://bikeworldlv.com', None, 'http://www.mathnasium.com/litchfieldpark', 'https://haircutmenbocaparklasvegasnv.com', 'http://www.partycity.com', 'http://www.donuttyme.com', '1592234787', '1592234790', None, None, None, '1592234800', None, 'http://www.scottsdaleaz.gov/parks/mountain-view-park', None, 'https://www.gowireless.com/stores/az/fountain-hills/fountain-hills-fountain-hills-plaza/', 'https://www.acesdental.com/areas-served/dentist-north-las-vegas-nv/?utm_campaign=yelpnlasvegas&utm_medium=organic&utm_source=local', 'http://www.rivierahotel.com/las-vegas-entertainment/crazy-girls.aspx', None, 'https://clevelandhomes.com', 'http://www.clipncleandoggrooming.org', None, 'http://www.centurylink.com', 'https://www.chick-fil-a.com/indianland', 'http://www.stabley.net', 'http://www.ledolci.com/', 'http://www.kemptonpt.com', 'http://www.bk.com', 'http://www.schneidersdairy.com', 'http://desertfoothillsgardens.com', 'https://aguayobunch.wixsite.com/a1electric', 'https://www.gianteagle.com/Stores/Store/?storeId=3043', 'http://www.chandlerpediatricdental.com', 'http://www.thereikigal.com', None, 'http://www.slepakinsurance.com?cmpid=RZYD_BLM_0006', None, None, 'http://www.colussy.com/?cs:pro=repman&cs:e=yelp', '1592234868', None, 'http://www.racersedgeperformance.com', 'http://www.waterconnectionaz.com', 'http://www.goindustrial.ca', 'http://www.bohofurnituregallery.com', 'http://www.dannysfamily.com/', 'http://www.sammysstudentexchange.com', 'http://bellagio.com/nightlife-diversions/hyde.aspx', 'http://thetoytank.com', 'http://www.ironcityarmory.com', 'http://journeyyogawellness.com', 'http://www.gatewayanimalohio.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=jan16', 'http://www.rocksolidconcrete.com', None, 'http://www.ajimenu.ca', 'http://www.precisionpoolcarellc.com', None, '1592234912', 'https://app.visionnv.com', 'https://www.calgarycoop.com/stores/shawnessy/', None, 'http://www.amcofh.org', 'http://www.ironoakshoa.com', 'http://www.z-teca.com', 'http://kendalaquatics.com', 'http://www.hunnerspizza.com', 'http://www.thedistrictatgvr.com/', 'http://www.apple.com/retail/glendale/', 'http://www.marquisdiagnosticimaging.com', None, 'http://www.thewirelesscenter.com', 'https://www.extraspace.com/storage/facilities/us/arizona/phoenix/501788/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'https://athleta.gap.com/stores/wi/madison/athleta-7080.html', 'https://www.usps.com/', 'http://katespade.com', None, 'http://www.nicksauto-tech.aaro.ca', 'http://www.hairmonet.com', 'http://www.greenwaymoving.ca', None, None, 'http://www.winemandental.com', None, 'http://www.mfmassage.com', None, 'https://bluepearlvet.com/hospital/avondale-az/', 'http://www.antheaspa.com', 'http://www.thechateauaz.com', 'http://www.coronetpizzeria.com', None, 'http://www.sabuddyrestaurant.com', 'http://www.avis.com', 'http://www.hendrickmotorsports.com', None, 'http://www.legacyjewelersofpittsburgh.com', 'https://www.dabuzispizza.com', None, 'http://alysskincare.com', 'http://vikingfishandchips.net', 'https://www.applebees.com/en/restaurants-champaign-il/2121-n-prospect-93091', 'http://www.thenailtique.com', 'http://www.shopsys.ca/', '1592235014', None, 'https://www.extraholidays.com/las-vegas-nevada/worldmark-las-vegas-boulevard?lid=yelp&utm_medium=referral-affiliate&utm_source=yelp.com&Identifier=yelp&hotelid=77219&utm_campaign=localpage-worldmarklasvegasboulevard&promoid=localpage-worldmarklasvegasboulevard', None, None, 'http://www.stmlv.org', None, 'http://www.purrclothing.ca', 'http://call4handymanlv.com', 'http://305kustomzdesigns.com', None, 'http://www.theoriginaldicksspeedotach.com/', 'http://visitpittsburgh.com', 'https://batlgrounds.com/axe-throwing-yorkdale', 'http://www.MyLasVegasChiropractor.com', 'http://www.planetdailies.com', 'http://liquorlibrarylv.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, 'http://tofoodfest.com/', 'http://snipssalonclt.com/', '1592235069', 'https://www.spencersonline.com/store/Ross-Park/32682040.uts', 'http://thestudioacademyofbeauty.com/locations/chandler-campus/', 'http://www.tinytots.ca', 'http://www.supremecollisioncentre.ca', 'http://www.mobilia.ca', 'http://www.westernexterminator.com/chandler', 'http://www.yorkmillspa.com', 'http://www.stampsautoqueencreekqueencreekaz.com', None, 'http://www.vitalitymwi.com', None, 'https://www.thespacelv.com', 'http://www.rosenbaumrealtygroup.com/', 'http://coolpools.services', None, 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://longwongsofnorthphx.com', 'http://www.winedowntc.com', 'http://www.mitcoremodeling.com', None, 'http://www.holdenarb.org/home/', 'http://kmedspa.com', None, 'http://www.quickerrooterplumbing.ca/', 'http://pittsburghrugcompany.com', 'https://suncountry.com', 'http://www.fujimiddleton.com', 'http://www.thebeergrowler.net/charlotte', None, 'https://sandpipers.ca', None, 'http://www.starbucks.com', 'http://www.picazzos.com', 'https://www.easystreetgalleria.com', None, None, '1592235155', 'http://www.goodlifefitness.com/locations/ontario/mississauga/toronto-pearson?source=yelp-websitelink-torontopearson-gl', 'https://www.pteglv.com/locations/pts-gold/st-rose-eastern/', None, 'http://www.weldrickanimalhospital.com/', 'https://www.cosmopolitanlasvegas.com/resort/spa?utm_source=yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.idotactical.com', 'http://www.progressive.com/locations/mayfield-heights-campus3/', 'https://elitevacuumsplus.com', 'http://www.vha.ca/', 'http://mwtravelvegas.com/', 'http://www.ezpawn.com/locations/nv/las-vegas/6032-cheyenne', 'https://www.eggsupgrill.com/locations/charlotte-nc/', 'http://www.popculture-comics.com', None, 'http://www.wimpysdiner.ca', 'http://www.shearshades.com', 'https://www.oroexpresschandler.com', 'http://www.forcesofnature.ca/', 'http://tommysdrivein.com', 'http://www.saintbernadette.com', None, 'http://steelcreationsfab.com', 'http://www.VerveStudio.net', 'http://www.performancemufflershop.com', 'https://po-ke.ca', None, 'https://www.usps.com/', 'http://grandcourtmesa.com', 'https://azfoodcrafters.com', 'http://www.ohiocitycycles.org', 'https://www.biltmorecounseling.com', 'http://www.budgetmoversaz.com', 'http://bluewavepoolsaz.com', 'https://www.haggar.com/stores/las-vegas-nv/?utm_campaign=websitelink&utm_medium=Referral&utm_source=yelp', None, 'https://www.coultertempe.com', 'http://www.swimzone.info', 'http://walmart-eyedocs-lasvegas.com/Eastern-Russell', None, 'https://www.calgarypromovers.com', 'http://www.gyrotime.com', 'http://www.dinaalonzibridal.com', 'http://www.massagelifewellness.com', None, 'http://www.shellhospitality.com', None, 'http://www.lakemetroparks.com/parks-trails/farmpark', 'http://www.charlottegeneraldentist.com/', 'http://tomyumthaiaz.com', '1592235283', '1592235286', 'https://www.30sixnoda.com', None, 'https://www.laserquest.com/on-whitby', 'https://yogatothepeople.com/tempe-az/', None, 'http://hairbygk.com/', 'http://www.crookedcue.ca/', None, 'http://www.mission4th.ca', 'http://www.lisatrainer.net', 'http://www.greektownrestaurant.com', None, 'http://arizonasports.com', 'http://www.itmp.com', None, 'http://www.scarboroughnissan.com', None, 'https://www.walgreens.com/locator/walgreens-401+w+main+st-waunakee-wi-53597/id=5669', 'http://www.andrewsco.com', 'https://www.sheridancollege.ca', 'http://www.bloombrossupply.com/', 'https://www.esso.ca/en/gas-station/richmondhill-on-beavercreekesso-200302403', 'http://www.eatatgreenmix.com', 'http://www.seasonsboulangerie.com', 'https://tanwithkare.com', '1592235353', None, 'http://bestnails.webs.com/', 'http://Brilliantnailsspa.com', None, 'http://www.lowes.com', '1592235367', 'http://www.lasvegascaralarms.com', 'http://scottsdaleshadowsarizona.com', None, 'http://www.jjcontractingnv.com', 'http://www.dualimagesmiles.com', 'https://agents.allstate.com/j-c-alvarado-charlotte-nc1.html', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://mnandipies.com', None, 'http://www.ArnoldSmithLaw.com', 'http://www.customcobblersofmadison.com', 'https://stores.anntaylor.com/nv/las-vegas/1013-south-rampart-blvd.html', 'http://www.suncityupholstery.com/', None, 'http://www.dropshade.com', 'http://popeyes.com/', 'http://gyro-spot.com', 'http://www.aircanada.ca', 'http://3apools.com/', 'http://www.associatedasset.com', '1592235418', 'http://www.terribleherbst.com/', 'http://www.studio262salon.com', None, 'https://ad.doubleclick.net/ddm/clk/434191077;236814625;i', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'http://www.mattressfirm.com', 'http://www.monkeypantsbar.com/', '1592235439', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://westvalleydentalaz.com/', 'https://abraauto.com/abra-auto-location/1051-charlotte-nc-albemarle-road', 'http://www.mrantenna.com', 'http://www.hlwp.co', None, 'http://www.sweetlifebakeshoppe.com/', 'http://www.brueggers.com/', 'http://footsolutions.com/strongsville', None, 'https://locations.dennys.ca/AB/CALGARY/248179', 'http://www.whitneymurphyfuneralhome.com', 'https://essencevegas.com/locations/henderson/', None, 'https://accutempaz.com', 'http://www.chefbar.ca/', 'http://www.mtlebanon.org/index.asp?NID=25', 'http://www.faregamecc.com', 'https://www.umcsn.com/Quick-Cares/Quick-Care-Locations-Summerlin.aspx?intMenuID=112&intPageID=197', 'http://www.safeworksillinois.com', 'https://www.hendrickhonda.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', 'http://www.access1alarm.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://vegasnailspa.com', 'http://sarahdiaz.com', None, 'http://www.theblackbullpub.ca', 'http://www.upmc.com/locations/community/family-health-centers/Pages/lawrenceville.aspx', None, None, None, None, None, None, None, 'http://www.vaughnautoglass.com', 'http://www.experttechauto.com', 'http://am.pizza', 'http://dennys.com', 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'http://www.themodclub.com/', None, 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://www.valleyfirefightermovers.com', 'https://www.choicehotels.com/north-carolina/charlotte/sleep-inn-hotels/nc005/rates', None, None, 'http://vcacanada.com/royaloak', 'http://dbarkadz-filipino-cuisine.business.site', 'https://www.chilis.com', None, 'http://nakedbeautybar.com/', None, 'http://www.lakesidespa.ca', 'http://www.trinitybellwoodsflea.com/', 'http://www.drcarolford.com', '1592235578', 'http://sinfulskinaz.com/', 'http://www.elxrjuicelab.com', 'http://www.laide.ca', 'https://totalstoragesolutions.com/storage-locations/arizona/peoria-storage-units/7590-w-olive-ave', None, None, 'http://www.ebgames.com', 'http://www.atomicdogboutique.com', None, 'http://www.championappliancecare.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.grafgrowers.com', 'http://www.gameworks.com/', 'http://www.septic-systems-calgary.ca/', 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', None, 'http://hmartca.com/hmart/?page_id=17', 'https://ad.doubleclick.net/ddm/clk/458685305;262921492;q', 'http://pastorcameron.com', 'http://www.leslievilledentistry.com/', None, 'http://joemommasgrille.com', 'https://www.cathaybank.com', 'https://www.verizon.com/home/storelocator/pa/pittsburgh-15206/', 'http://www.cartridgeworld.com', 'http://www.electricdaves.com', 'http://www.mistwoodapartments.com', 'http://daveandbusters.com/?utm_source=DB&utm_medium=Text&utm_term=DB&utm_content=WebsiteLink&utm_campaign=DB_DB_Text_WebsiteLink', 'http://www.callitspring.com', 'http://wreckamendedautobody.com', 'http://www.thisiscleveland.com', 'http://www.chevron.com', 'http://www.marijuanadeliveryline.com/shop', 'https://www.plantarestaurants.com/location/planta-queen/', 'http://www.kumon.com/SUMMERLIN', None, 'https://locations.wendys.com/canada/qc/lasalle/8699-boul.-newman', 'http://www.kabobnmore.com', None, None, 'http://www.kfc.ca/store/sunrige-mall-101-2525-36-st-ne-calgary', 'http://perpetualfitnesscle.com', 'http://sfdslv.org', None, 'https://whitesintegrityauto.com', None, 'http://www.tommiegirlphotography.com', 'https://www.sprint.com/storefronts/bd/sprint-phoenix-az-85022-fcs-1908/?ecid=SEO:Yelp:2020_Q1:LastMile', 'https://www.ceenta.com/locations/huntersville', 'http://flyingmonkeytruck.com', None, 'http://www.allysphotography.ca', 'http://www.nailganic.me', '1592235698', 'https://bailbondsusa.com', None, 'https://fullypromoted.com/locations/scottsdale-az/', '1592235706', None, 'https://www.localfirstaz.com/events/fall-festival', None, None, None, 'https://sugardaddyscafe.com', 'http://vitalitymds.com', 'http://www.muramoto.biz', 'http://www.7forallmankind.com', 'http://www.susysoup.com', 'http://treesbymikearizona.com', '1592235733', 'http://www.pilatesofcharlottenc.com', '1592235738', 'https://www.hungryhowies.com/store/hungry-howies-00876?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00876&utm_content=Website_Link', 'http://www.riddleroom.ca/', 'http://www.torchedgoodness.com/', 'http://www.precisionspecialtypharmacy.com', 'https://www.lhmnissanmesa.com', 'http://bit.ly/RealtyExecsTempeTower', 'https://smallpeoplepreschool.com', None, 'https://www.bobevans.com/our-restaurants/locations/571?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.wetzels.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=8658&localechange=1', None, 'http://Bundtsnbutter.com', 'http://www.arizonajewelryappraisals.com', 'http://paisleymonkey.com', 'https://www.euroworks.ca', 'http://www.maltzmuseum.org/', 'http://www.akronphotographer.com', None, 'http://www.firegrill.com/', 'http://www.hairoriginalsalonstudio.com', 'http://azdollhouse.com/', 'http://www.gracelutheranhenderson.org', 'http://thepopplacestore.com', None, 'http://www.widmaierchiropractic.com', None, None, 'http://www.toronto.ca/parks/prd/facilities/complex/287/index.htm', 'http://tokyodiscountvegas.com', None, None, None, None, 'https://www.redrobin.com', 'http://www.pranjbeauty.com', None, None, 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://www.structube.com', 'http://popeyes.com', 'http://in.puma.com', 'https://www.discounttire.com/store/az/gilbert/s/1418?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', '1592235832', 'http://totum.ca', None, None, 'http://www.bestofthebestdjs.com', None, 'http://www.gungarage.com', 'http://www.sunsetvillaaz.com', 'http://cornerstonegiftsandpo.com', None, None, None, 'http://calibercollision.com/locate-a-caliber-collision-center/surprise', 'http://www.desertstorage.com/scottsdale-az-storage-units', 'http://www.scottsdalecc.edu', 'http://www.cupkateslv.com', 'http://www.caesarspalace.com/restaurants/empress-court.html#.Ugfc5su9KSM', 'http://www.brossardbagel.com', 'http://www.mrchickencle.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://locations.avis.com/us/az/chandler/ca3.html', 'http://www.modoyogalasvegas.com', '1592235882', '1592235884', 'https://www.valleyhealthphysicians.com/find-a-doctor/hazem-afifi', 'http://Surprisecomics.com', 'http://www.smileycrane.com', None, 'http://allstateappliancelv.com/', 'http://johnnyrockets.com/', None, 'https://www.mesaparks.com/parks-facilities/parks/countryside-park', 'http://www.monarkhome.com/showrooms/las-vegas', 'http://www.steinmart.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/109+Dabney+Drive-Henderson-NC-27536/storeid=7055?cid=ps_ylp_2020', 'http://www.dillonazrealty.com', 'http://www.arizonaplumbingservices.com', '1592235919', 'http://www.lasvegaspilatesyoga.com', 'http://www.deeppilates.com', 'http://www.irepairicustomize.com', None, 'https://www.hilton.com/en/hotels/clttght-home2-suites-charlotte-i-77-south-nc/?SEO_id=YELP-HT-CLTTGHT', 'http://www.capitalacctpc.com/', None, 'http://www.jamminjumperoos.com/', '1592235936', 'http://www.frozen75.com', 'http://Tamerabbit.com', 'https://bounceu.com/gilbert-az', 'http://www.bullseyesvc.com', None, 'http://popeyes.com', 'http://www.fastfreshfoods.ca/', None, 'http://www.palmsouthwest.com', 'http://www.jeguitars.com', 'http://www.carrefourrichelieu.com/fr', None, 'http://Www.2womenandasolution.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___maryland', 'http://www.RobinsonAutoDetails.com', 'https://stores.fossil.com/az/gilbert/santan-village-8252/', None, '1592235970', 'http://www.cleveland.hfitcenter.com/', 'http://www.bk.com', 'http://phoenixcoffee.com', None, None, None, 'https://www.lovencarevet.com', 'http://www.saintjohncathedral.com', 'https://www.ryokujudo.com', None, 'http://www.tacotimecanada.com/locations/ontario/ajax/ajax', '1592235997', None, 'http://qdoba.com', None, 'http://roomsonline.ca', 'http://www.prada.com/', 'http://www.cigna.com/cmgaz/locations/san-tan-medical-office', 'http://www.innergroovebrewing.com', 'http://www.drtorgerson.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://freshandclear.com', 'http://www.starbucks.com/store/9298/', None, 'http://www.kingbalancing.com', None, None, 'http://www.atlwings.com', 'http://www.cuttyfresh.com', 'https://cleancutlandscaping.us', 'http://www.luxuryhomesofhenderson.com', None, 'http://www.sagebrushranch.com/', 'http://snapfitness.com/waxhawnc', 'http://www.bergo.ca', 'http://www.smilesavvydentistry.com/', 'https://www.purebarre.com/location/dana-park-az', 'https://www.hooters.to/toronto-airport', 'http://www.zenq.ca', 'http://www.drshaunachristensen.com', None, None, 'http://www.kingflyspirits.com', 'http://www.theradiodoctor.com', 'https://www.tirediscountdepotinc.com/cleveland', 'https://www.bobevans.com/our-restaurants/locations/357?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.strattonrestoration.com', 'http://www.Liorthebaker.com', 'http://rmtmassagetherapytoronto.com', None, 'http://fiscalfitnessphx.com/', 'http://banderarestaurants.com/locations/scottsdale/', 'https://www.state48brewery.com', None, '1592236095', 'http://www.quiktrip.com', 'http://www.almikestavern.com', 'http://www.earnhardttoyota.com', 'http://www.clairhursteyecare.com', 'http://mybodyworkz.com', 'http://www.envoquemd.com/', 'http://rvcomplete.com', None, 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store48', 'http://www.familyfocusedeyecare.com', 'https://www.obonsushi.com/scottsdale-quarter', None, None, 'https://www.choicehotels.com/arizona/youngtown/quality-inn-hotels/az453/rates', 'http://pizzeriaenzo.com', 'http://www.fitzgeraldsbnb.com', 'http://www.steeltownpaintball.com', '1592236142', 'http://www.timelesstattoolv.com', 'https://www.starbucks.ca', None, 'http://www.landmarkworldwide.com/customerservice?utm_source=yelp_sea&utm_campaign=support&utm_medium=website&utm_content=https', 'http://www.southtowndentalcare.com/', 'https://shinynailsonhappyvalleyglendale.com', 'http://www.foothillsrehab.com/', 'http://www.kay.com', None, 'http://www.azcustomhats.com', None, 'http://www.gokartsatpolsonpier.com', 'https://www.jamesacarytreeservice.com', 'https://artscommons.ca/rentals/venues/max-bell-theatre/', 'http://www.medoneaz.com/', 'http://www.destinocalgary.com/', None, 'http://www.futureshop.ca/', 'http://www.thingsremembered.com', 'http://www.restoamir.com/', 'http://www.kay.com', 'http://www.sunguntanning.com', None, 'https://www.scottsdalemusicaltheater.com', 'http://www.terrysauto.extremewrench.com', None, 'http://www.tupelohoneyteas.com', 'http://www.cliftonmartini.com/', 'http://www.oddballpets.com', None, 'http://www.lcbo.com', 'http://www.azrollerderby.com', 'https://www.chilis.com', 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6038', None, 'http://thecornerspot.ca', 'https://www.wyndhamhotels.com/hotel/03733?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:03733', 'https://stores.bareminerals.com/az/chandler/us-3/', 'http://deluxenailsbar.com', 'http://www.watsonsglen.com', None, 'http://www.2andhighbar.com', 'http://www.alpineroofing.ca', 'http://www.klingshirnwine.com', 'https://www.theranchestates.com', None, None, None, 'http://www.crowntownathletics.com', None, None, None, 'https://www.westgateresorts.com/hotels/nevada/las-vegas/westgate-las-vegas-resort-casino/', 'http://www.marshallsonline.com/store-finder/204', 'https://www.bellamirageapts.com', 'http://www.dvpeds.com', None, 'http://sololiquor.com', None, 'http://www.shampoochgrooming.ca', 'https://keepitcut.com', None, 'http://www.benjerry.com/', None, 'http://www.weissmeats.com', 'http://www.thegreenhouseflorist.com', None, 'http://www.halecoffee.com', 'http://www.mycompletepoolcare.net', 'http://www.ranchodetiarosa.com/rancho-chandler.asp?expanddiv=all', 'http://www.mokshayogaaurora.com', 'http://mrlube.com', None, 'http://www.textbookpainting.com', 'http://www.hansenortho.com', 'https://www.highlandparknorthlake.com', 'https://www.ulta.com/stores/madison-ms-477', 'http://www.saltrivereyecare.com', None, 'http://www.knuckledownsaloon.com/', None, 'http://www.westsidemarket.org/vendor.aspx?id=69', None, None, 'http://deseretindustries.org', 'http://www.marcs.com/stores/marcs-north-ridgeville-grocery-store-44039.aspx', None, None, 'http://www.phoenix.edu', None, None, 'https://www.marcos.com/locations/nc/gastonia/w-garrison-blvd', 'http://www.steelcityflooring.com/', 'https://vrjunkies.com/vr-junkies-az/', 'http://sears.com/stores/massachusetts/cambridge/0001343.html', 'http://www.legionbrewing.com', None, None, 'http://www.dukesbread.com', None, 'http://www.jellybeenz.com', 'http://www.urbanbean.ca', None, 'http://www.labellavitacleveland.com', 'http://www.sash.ca', 'https://www.choicehotels.com/CN659?mc=blypypaf', 'http://www.aceparking.com/downtown-phoenix-parking.com', 'http://www.careytechsolutions.com', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'http://armorpestdefense.com', 'http://www.heidisbrooklyndeli.com', 'http://ilanmassagestudio.com', 'http://bdcustomtattoos.com', 'http://www.ntb.com/store/6234/mayfield-heights-oh-44124-2905?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, None, '1592236410', None, '1592236415', None, 'http://www.hightails.ca', 'https://www.agelesskarate.com', 'http://www.mpautobodyrepair.ca', 'http://www.carlstreeservice.net', 'http://www.tailoredeventslv.com', None, '1592236432', 'http://www.solairespa.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.exosathome.com', 'http://dentalbobw.wix.com/denturerepairs', 'https://www.sleepez.com/?utm_campaign=Yelp&utm_source=yelp&utm_medium=referral', 'http://hamiltonortho.com', 'http://www.rbinc-sports.com', 'https://www.pikebeverage.com', 'http://ccandcompanysalonspa.com/', None, 'https://www.cleanjuice.com/locations/uptown/', 'http://srwc.unlv.edu/', 'http://www.theronceyhotel.com/home.html', None, None, 'http://www.702-pools.com', None, 'http://www.belmontapts.com', 'https://www.thehealingquest.com', 'http://robertostacoshop.com', 'http://www.charlottegolf.com', 'https://www.haircutmencorneliusnc.com', None, 'http://www.tymaz.com/', None, None, None, 'http://www.coquettepatisserie.com', None, None, 'http://www.alisfashion.com', None, 'http://www.yogurtys.com', 'https://torontoanimaleyeclinic.com', None, 'http://www.teamrossman.com', 'http://www.firehousemovingco.com', None, 'http://constanthomecomfort.com', None, 'http://www.wcequestrian.com', 'http://warehousewars.net', None, None, 'http://www.baselineflowers.com/', 'http://luccaclothing.com/', 'http://www.ilovekickboxing.com/kickboxing-studio/index.php?id=374?utm_source=review&utm_medium=yelp&utm_campaign=referral%C3%8A', 'http://www.azdmovers.com', None, None, 'http://www.harveycatshotel.com/', 'http://www.bk.com', 'https://www.allinclusiveconcretesystems.com', 'http://www.raintreerestaurantchagrinfalls.com/', 'http://nisstech.com', None, 'http://www.ciaociaopizza.com/', 'https://www.bestcharlottemassage.com', 'http://www.LisaYoungDDS.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=1962&localechange=1', 'https://fullpoolservices.com', 'http://www.theparlorlv.com', None, 'http://tonysautoworks.net', None, 'http://nolinesbydesign.com', 'http://local.buckle.com/AZ/GLENDALE/331/?utm_source=Buckle&utm_medium=Website&utm_campaign=Store+Locator', None, '1592236581', None, None, 'http://wyattorthodontics.com', 'http://www.staxburgerbistro.com', None, 'http://www.progressivepavers.com', 'https://www.storagewest.com/facilities/baseline/?utm_source=YelpCTA&utm_medium=referral&utm_campaign=baseline-business', 'http://www.crowdpleezersbarbershop.blogspot.in/', 'http://www.AltierDental.com', 'https://www.victoriassecret.com/store-locator#/store/442', 'http://www.wickedclub.com', None, '1592236611', 'http://www.containerstore.com/locations/showStores.htm?zipCode=28211&searchArea=100', None, None, 'https://lljcustoms.com', None, 'http://www.kohakitchen.com', 'https://locations.wendys.com/united-states/pa/bridgeville/1125-washington-pike', 'http://toba.ca/', None, None, None, 'http://www.renue.ca', 'http://www.mobilehomedepot.net', 'https://www.rubytuesday.com/', 'http://www.odiagasautosales.com', None, None, 'http://www.rivieraopticare.com/', 'http://www.showcasemotorspa.com/', None, 'http://www.azsleepyteepee.com', 'http://giantjones.com', None, 'http://www.marcos.com/locations/oh/berea/w-bagley-rd?s=true', 'http://www.pimadental.com', None, None, None, 'https://www.centerforsightlv.com', None, None, 'http://stores.bestbuy.com/122/', None, 'http://www.averyonthegreen.com', 'http://www.krispykrunchy.com/locations/wy-market', None, 'http://www.thecamptc.com/location-gilbert', 'http://www.saigonpearl.ca', 'http://www.posaresalons.com', 'http://www.sanrio.com', 'http://Islandstylepools.net', 'https://turningpointbeauty.com', None, 'http://www.reneesmassotherapy.com', 'http://johnnyrockets.com', None, 'http://funkytoque.com/wellington-accueil/', 'https://www.smithsfoodanddrug.com/storeHours?store=70600354', None, 'http://therabbitspot.com/the-rabbit-hole/', 'http://www.psdm-madison.com', 'http://www.tizzerts.com/', 'http://flahertytree.com', 'http://www.saddlebroncgrill.com', 'http://www.dwmeats.com/', 'http://www.malleys.com', 'https://www.sprint.com/storefronts/bd/sprint-goodyear-az-85338-d-8157/', 'http://expertcarcareandtransmissions.com', 'http://www.themakeden.com/', None, 'http://www.arbys.com', None, None, None, 'http://www.cupcakejunkiecafe.ca/', None, 'http://www.carolinascornerstone.org', None, 'http://joinswift.com/landing-pages/DR/student/yp/careerhorizon/lp', 'http://monogramcoffee.com', 'http://www.littlecaesars.com', None, 'https://www.fastmed.com/urgent-care-centers/scottsdale-az-walk-in-clinic-mcdowell-road/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.stagsfamilychiropractic.com', None, 'http://www.luxhairsalon.com', 'http://www.fiveguys.com', 'http://www.smittys.ca', 'https://locations.dennys.com/MO/INDEPENDENCE/248531', '1592236785', 'http://www.wellnessmedspacosmetics.com/', 'http://sungshouse.com', None, 'http://www.gaatithaikitchen.com', 'http://www.starbucks.com/', 'http://www.augustoalgusto.com/fr/', None, 'http://www.thegroceryohc.com', 'https://www.mcalistersdeli.com/locations/il/peoria/4810-north-university-street-1289?utm_campaign=yelp&utm_medium=referral&utm_source=yelp&utm_content=1289', 'http://www.kangsbba.com', 'https://www.4patientcare.ws/wsv3pro/web/webschedulerv3.aspx?SessionID=2050207', 'http://noahsarkpediatrics.com/', 'http://eosfitness.com/location/north-scottsdale?utm_campaign=north-scottsdale&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', 'https://www.jandbhauling.com', 'http://goodboydogs.ca', None, 'https://www.tajo-one.com', 'https://www.barkbusters.com/dog-training-charlotte-south', 'http://studiobell.ca', None, 'https://stores.jcrew.com/en/crocker-park?srccode=X%7CPMG%7CNaturalSearch%7CLocal%7CYelp%7C677', None, 'http://www.allseasonsmaintenanceandlandscaping.net/', 'http://www.reborncabinets.com', 'http://mikadosushirobata.dining.ca', 'http://www.orchidspa.net/', None, 'https://www.rolandswigsalonmatthews.com', 'http://www.vegashottubs.com', 'http://hammertoronto.com', None, 'http://www.badassjacks.ca', 'https://www.hilton.com/en/hotels/phxmdgi-hilton-garden-inn-phoenix-midtown/?SEO_id=YELP-GI-PHXMDGI', 'https://www.180smoke.ca/vape-shop-etobicoke-islington-electronic-cigarettes', None, 'http://www.burtonstudio.vegas', 'http://mississaugabarbershop.com', None, None, 'http://www.terribleherbst.com/', None, 'http://www.alovingleash.com/', None, 'http://emeraldcomputers.com/', None, 'http://www.cookout.com', 'http://www.acupuncturecenteraz.com/', 'http://www.TheKyotoBowl.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216347&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://skintologyrx.com', 'http://leafandplate.tumblr.com', 'http://www.ballyslasvegas.com/restaurants/sea-the-thai-experience.html#.UkB2BsZnGoM', 'http://www.beinlovedesigns.com', 'https://www.athome.com/store-detail/?StoreID=Pennsylvania-Pittsburgh&utm_source=yelp&utm_medium=paidprofile', 'https://locations.theupsstore.com/pa/white-oak/1985-lincoln-way?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://eclipseautobody.com/', None, None, 'http://www.saltchaletarizona.com', '1592236923', 'http://www.rlemb.com', None, 'http://earlymercy.com', 'http://www.lpmproduction.com', 'http://www.nobullburgers.ca', None, None, 'http://www.wilsonstaekwondo.com', 'https://www.autozone.com/locations/az/avondale/10815-w-indian-school-rd.html', 'http://www.chilis.ca', 'http://eighteeneight.com/north-scottsdale-az/?utm_source=yelp&utm_medium=organic&utm_content=weburl', None, 'http://www.zenlia.com', None, None, 'http://www.bowwowdoggiedaycare.com', 'http://www.teakwoodstavern.com/', 'https://rolliciouscreamery.com/madison-1', 'http://www.goldcoastcasino.com', 'http://www.beinsoccer.com', None, None, 'http://www.vegasthedj.com', 'https://local.fedex.com/oh/mayfield-heights/office-1225/', 'https://stores.golfgalaxy.com/nc/charlotte/3039/', 'https://www.positivelyfrosted.com', None, 'http://www.azactorsacademy.com', None, None, 'http://www.rockymountainsoap.com/', 'https://pracharlotte.com/location/charlotte-cotswold-eastover/', 'https://www.taravietnamesegrill.com', None, 'http://www.ubreakifix.com/locations/pittsburgh', None, 'http://www.splaw.net/', 'https://www.olivegarden.com/locations/az/mesa/southern-fiesta-mall-west-mesa-alma-school-rd/1661?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:mesa-az-1661_pl:locurl_rd:1517', 'http://www.portofsubs.com/', None, None, 'http://www.concentra.com', 'https://www.deshonpullenlaw.com', 'http://www.mcfarlandlibrary.org/', 'https://www.wellsfargo.com', 'http://www.LegalRide.com', '1592237028', 'https://www.trainerpaul.com', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', '1592237043', 'http://www.cefiore.com', 'http://www.roncesvallesanimalhospital.com/', 'http://jokercafe.info/', 'http://www.traderjoes.com', 'http://www.alohayogurt.com', 'http://www.outdoorlivinglv.com', 'http://www.litespressobar.com', None, 'http://www.mikesgranite.com', None, None, 'https://www.spectrumoralandfacialsurgery.com', None, 'http://www.mpi-services.com/', None, 'http://www.senseandcolor.com/weddings', 'http://gexwomenscare.com/', 'http://www.alleghenyvet.com', 'http://www.reclaimedsecrets.com', 'http://www.desertskyfamilydental.com', 'http://www.greenleafarrowheadranch.com', 'http://www.discount-drugmart.com', 'http://www.trueshinerimrepair.com', 'http://www.brars.ca', 'http://www.eagleindustriescorp.com', 'http://www.discountcab.com/', 'http://muddypawslv.com', 'http://cherryontop.net/', None, 'https://www.zoup.com', 'http://www.beckseuropean.com', 'http://www.ejsushi.com', 'https://locations.monro.com/pa/crafton/2175-noblestown-rd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://egl-junk-removal-lasvegas.business.site', 'http://pandora.net', None, None, 'http://www.drpease.com', 'http://www.zimbrickbuickeast.com', 'https://www.gessweinsclocks.com', 'https://www.huntington.com/Community/branch-info?locationId=625', 'http://www.tremontmusichall.com/', None, 'https://killumpestcontrol.com', None, 'http://fitnessconnection.com/clubs/southpark/', None, 'http://smiledocsaz.com', 'http://www.pinkislaserspa.com', 'http://www.empowerpt.com', '1592237155', None, 'http://www.artofshoerepair.com', 'http://www.starbucks.com/store/1013599/', 'https://www.londondrugs.com/london-drugs-store-030-calgary/heritage-plaza-030.html', 'http://www.libertymutual.com/brian-weaver', 'http://www.beansproutscafe.com', 'http://www.capitalone.com', 'http://www.kidzrockprep.org', 'http://www.lvsurgical.com', 'http://goharvestmarket.com', '1592237180', 'http://www.scottsdaleautosalon.com/home', 'http://www.studioadt.com/', 'http://www.bamdogwash.ca', 'http://www.staytruebodyart.com', 'http://www.liveatthepavilions.com', 'http://www.restaurantkarma.com', None, 'http://ifadevegas.com', 'http://www.loirerestaurant.ca/', 'http://www.flrpropertymgmtphoenix.com/', 'http://www.mrchickencle.com', None, 'http://cibronebakery.com/index.html', 'https://locations.timhortons.com/ca/on/richmond-hill/1070-major-mackenzie-dr.html', None, None, 'http://www.newlookhairnailandspa.com', 'https://www.elitemusic.ca', None, None, 'http://pageskensington.com/', 'https://www.bobevans.com/our-restaurants/locations/266?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.deseretfamilymedicine.com', 'http://algobertoslasvegas.onlunchroom.space', None, 'http://www.prettyyongething.com', 'http://www.solarpenny.com', 'http://www.southernnevadalocksmith.com/', 'http://www.wongsphoenix.com', 'http://www.dsw.com', 'https://palmbeachtan.com/locations/AZ/Peoria-West-Thunderbird-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'https://mountainsidefitness.com/locations/gilbert/', None, 'https://ad.doubleclick.net/ddm/clk/434177199;236814625;r', 'http://stlouiswings.com', None, 'http://www.posaresalons.com/', 'http://actionappliances.net', 'http://www.riteawayservices.co', None, None, None, 'http://www.buymaytag.ca', None, 'http://www.zibabeauty.com/', 'http://www.eternalhealthandwellness.ca', 'http://hoangthynailsspa.com/', 'http://www.kimmyztatumpoint.com', 'http://www.fisherkingwinery.com', 'https://lasvegas.colormemine.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.surlatable.com/browse/storeCalendar.jsp?storeId=137', None, 'http://www.spalv.com', 'http://www.fhtaz.org', 'http://www.shell.com', 'http://hgsystemintegrators.com', 'http://littlawfirm.com/', None, 'https://duckdonuts.com/locations/huntersville-nc-rosedale-shopping-center/', None, 'http://pittsburghpetgrooming.com', 'http://www.drkintonis.com', 'http://www.daniadown.com', None, 'http://www.azrealtycare.com/', 'http://www.basspro.com/webapp/wcs/stores/servlet/CFPageC?storeID=55&storeId=10151&langId=-1&catalogId=10051&tab=3&appID=94', 'http://www.omgbakedgoodness.com', None, None, None, 'https://www.usps.com/', 'http://drupatis.com', '1592237356', 'http://www.launicahuntersville.com/', 'http://www.ardene.com', 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=187&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-187', 'http://yourazbraces.com', 'http://www.parkwaychiropractic.net', 'https://cutrateglass.com', '1592237372', 'https://www.kohls.com/stores/nv/lasvegas-669.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.centropolis.ca', None, 'http://www.mvnailspa.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.wildwestmercantile.com/cgi-bin/Category.cgi?category=home&type=store', 'http://www.rosetuxedoaz.com', 'http://www.starbucks.com/store/9681/', 'https://www.therange702.com', 'http://www.mccalls.ca', 'http://www.chefkebab.ca', 'http://drjsoffice.com', '1592237404', 'http://www.waterjack.com', 'http://gonyfl.com', 'https://www.walgreens.com/locator/walgreens-275+davison+dr-sun+prairie-wi-53590/id=3291', 'http://www.kwalitysweets.com', 'http://velocitycx.com/', 'http://www.carolinashealthcare.org/cabarrus-pediatrics-map-and-directions', 'http://www.sheawomenscare.com', 'https://www.anytimefitness.com/gyms/2744/University-Heights-OH-44118/?utm_source=yelp&utm_medium=local', None, 'https://signup.myiclubonline.com/iclub/newAgreement/0389/selectPlan.htm', 'http://www.yogurtvi.com', 'http://www.venetian.com/nightlife/bars-and-lounges/the-bourbon-room.html', 'http://tropicaldelightscharlotte.com/', 'http://www.countryinns.com/champaignil', '1592237438', None, 'http://www.thecandybar.ca', None, 'http://www.pdqstores.com/gmaps/Wisconsin/MadisonArea/135.html', None, 'https://pho-fordays.com', None, 'https://www.sonoraquest.com/find-a-location/glendale-59th-ave-eugie/', 'http://www.queencitytours.com', None, None, 'http://www.atriasunlake.com', 'http://www.duetcatering.com', 'https://www.target.com/sl/charlotte-midtown/2244', 'http://www.starbucks.com/store/9298/', 'https://www.chick-fil-a.com/arboretum', 'http://marusakebar.com/', None, 'http://www.salazarusedcars.com', 'http://www.arizonadeck.com', None, 'http://www.jerusalemgrill.com', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://www.drtarapeyman.com', '1592237494', None, 'http://www.redcareers.com/kwrpp/', 'http://www.spiedini.com/', 'http://www.marvelousepoxyflooring.com', 'https://order.littlecaesars.com/en-us/stores/15150003/10720-e-southern-ave/mesa/az/menu', None, 'https://bhmanagement.com/communities/the-venue-on-camelback/', 'http://www.greencardadvice.com', 'http://erabyciara.com/', 'http://www.zocalobistro.com', 'http://tyrell710.wix.com/fingertips2thesoul', 'http://www.marshallsonline.com/', 'http://650cafe.com/', 'http://www.astaraskincare.com', 'http://www.arrowheaddermatology.com', '1592237535', 'http://www.serviceking.com/locations/service-king-penn-hills?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://locations.michaels.com/az/mesa/2778/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.centurylink.com', 'https://locations.jackinthebox.com/us/ca/concord/1710-monument-blvd', None, 'http://www.dads-smokeshop.com', 'http://www.friendlyneighborhoodhelp.com', 'https://www.olivegarden.com/locations/oh/parma/parma-town-mall/1128?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:parma-oh-1128_pl:locurl_rd:1083', 'http://www.beautifulskinbylucy.com', 'http://www.ritasfloraldesigns.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.arcelectriccompany.com', 'http://www.7-eleven.com/?yelp=29384', 'https://locations.massageenvy.com/arizona/scottsdale/8752-east-shea-blvd-ste--c-3b.html', None, None, 'https://redrock.sclv.com/Gaming/Race-and-Sports-Book?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', 'https://www.target.com/sl/las-vegas-blue-diamond/2164', 'https://www.arashijapansteakhouse.com', 'http://www.mgpaz.com', 'http://www.silversnail.com', None, None, 'http://www.ajsfinefoods.com', 'http://www.lasvegasguitarteacher.com', 'http://www.trilogypoolsaz.com/', 'http://poshpooches.ca', 'http://www.aleromoving.com/', None, 'http://www.litchfieldauto.net', 'https://www.crowncustomtattoo.com', 'http://www.illinismilesdental.com', None, 'http://www.udallattorneys.com', 'http://www.rvmastertechs.com', None, 'http://www.buffaloscafe.com', 'http://www.bengioielli.com', None, 'http://www.moulinbouge.com', 'http://birkdalevillage.net/portfolio/birkdale-village-cleaners', 'http://Munhallvet.com', 'http://www.hillhurstmortgage.com', 'https://www.zaxbys.com/locations/sc/fort-mill/3401-hwy-21/', None, 'https://www.bestwestern.com/en_US/book/hotel-rooms.03157.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03157', 'http://ilfornello.com/richmond-hill/', None, None, None, '1592237668', 'http://www.bigotires.com/regions/minneapolis-metro', None, None, None, 'http://Www.electrikneedletattoo.com', 'http://www.apachetaxi.com', 'http://www.ibdaz.com', 'http://www.gfsbjj.com/', None, 'http://www.matthewsalehouse.com', 'http://www.antoniospizza.net', None, 'http://eastvalleyurban.com/phoenix/stella', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://DDLDental.com', 'http://familydentalstudio.net', None, None, 'http://www.friendsofthewild.org', 'http://www.libertymutual.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.einsteinbros.com/', 'http://www.paradisebaypetresort.com/', 'http://www.everlastingchanges.com', 'http://www.quiktrip.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://thebeatbooth.com', 'http://babycakeswilloughby.vpweb.com', 'http://www.arizonastone.com', 'http://www.newdirectionfertility.com', 'https://www.vegaslashlounge.com', '1592237755', '1592237758', 'http://www.thecurzon.ca', None, 'http://www.samsbarbershops.com', 'http://www.imeldasmith.com', 'http://tinkers-handyman-service.business.site', 'http://www.starbucks.com', None, None, 'http://www.shaggyshaggyshake.com', None, None, None, None, None, 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', None, None, None, 'http://pho87.net', None, 'http://poolpartsplus.net/', 'https://www.dominionselfstorage.net/self-storage/az/queen-creek/dominion-self-storge-queen-creek/unit-sizes-prices', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Las%20Vegas/NV/8114', 'https://www.greatvaluestorage.com/self-storage/las-vegas-nv-92971', 'https://konjikiramen.com', 'http://yackodentistry.com', 'https://www.podiatryinc.com', 'http://www.freewayinsurance.com', 'https://chocolateshops.sees.com/az/phoenix/chocolate_shops_phoenix_az_102103.html', 'https://acesandarrows.com', 'http://www.noisette.ca/index.html', 'https://locations.cinnaholic.com/ll/CA/ON/Scarborough/6015-Steeles-Ave-E', 'https://www.sunnysidehonda.com', None, None, None, 'http://www.bwsweetsbakery.com', '1592237855', None, 'http://www.charlotte.studio-cellar.com', 'http://www.xooro.com', 'https://www.sonoraquest.com/find-a-location/phoenix-by-appointment-only-tatum-shea/', 'https://www.cellphonerepair.com/charlotte-uptown-nc/', 'https://ad.doubleclick.net/ddm/clk/458685299;262921492;c', 'http://www.somunsuperstar.com', '1592237871', 'http://www.archeryhq.com', 'https://www.agoracleveland.com', 'http://victoryenergywellness.com/', 'http://www.geeksnthings.com', 'https://nodabrewing.com', None, 'http://phoenix.sentrymgt.com', 'http://www.caringheartsanimalclinic.com', 'http://www.stellavapors.com', None, 'http://www.prohibitionclt.com/', 'http://scenicbrewingcompany.com', None, None, None, 'http://justpuckit.com', 'https://www.avioflower.com', 'http://www.bbhairringtons.com', 'https://www.olivegarden.com/locations/oh/north-olmsted/north-olmsted-great-northern-mall/1133?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:north-olmsted-oh-1133_pl:locurl_rd:1087', 'http://www.chousky.com', 'https://speedstarautotransport.com', 'http://www.kolornkiln.com', 'https://www.b1locksmith.com/chandler-locksmith', 'http://www.gamestop.com', 'http://www.gamestop.com', 'http://www.littlecaesars.com', 'http://www.fetaolivesgrill.com', 'http://pittsburgh.vettechinstitute.edu', 'http://luna-street-food.business.site', 'http://centurymill.com', 'http://www.BeestungLingerie.com', 'http://www.rapunzelhair.ca', 'http://www.reliableautolv.com', 'http://extremevaluestore.com/', None, 'https://www.happyaxe.com', 'https://kipc.vegas', None, None, None, None, 'http://www.coastappliances.com', 'http://www.phoenix.egoscue.com', 'http://www.bartonsbakeshop.com', 'http://www.banfield.com/veterinarians/wi/madison/emn?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.homehardware.ca/en/dealer-microsites/1274-8/contact-information.htm', 'http://www.europeanmotorstudio.com', 'https://wildfire.sclv.com/The-Greens', 'http://www.boosterjuice.com/', '1592237980', None, 'http://uniquepatiocreations.com', 'http://www.wexlerstavern.com/', 'http://theplacearizona.com', None, 'http://www.mtlebanonfloral.net/?srccode=yelp_track', '1592237997', 'https://thepetclub.com', 'http://www.encompasshealth.com', 'http://www.dimanddensum.com/', 'http://www.wingatehotels.com/hotels/hotel-overview?wid=ps%3Aaddppc_yelp&tel=18885953511&reg=appc-_-YLPROPP-_-30442-_-winwes&hotel_id=30442&cid=whg_winwes_yelp', 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', 'http://lasvegassolarinstallation.com', 'http://www.hairpieceslv.com', 'http://www.thecharlestondtlv.com', '1592238018', 'https://www.caferio.com/locations/eastern', 'http://www.skysalon.com', None, 'http://www.tourneau.com/custserv/locate_store.cmd?storeNumber=33', 'https://www.bootbarn.com', '1592238033', 'http://www.modelcitizentoronto.com/', 'http://www.epiphanychandler.org', 'http://www.trueblueautomotive.com/', 'https://www.anatomica.ca', 'http://churchschicken.ca', 'http://facialsbysofia.com', None, 'http://www.davidesbakeryandcafe.com/', 'http://www.calgarygold.ca', 'http://www.laroccaspizzeria.com', 'http://www.rowhousecinema.com', 'http://www.buddhapie.ca', '1592238062', '1592238065', 'http://www.sunshinegrandcanyon.com', 'http://www.handysacehardware.com', 'http://www.honeybutterbakery.com/', None, 'http://carrepairvegas.com', 'http://www.tortoiseandharesports.com', None, None, 'http://www.buyerschoicelv.com/', None, None, 'http://www.erieislandcoffee.com', 'http://www.baytowne.net', 'https://www.sephora.com/happening/stores/gilbert-san-tan-village', None, '1592238099', 'http://www.glendaleca.gov/', 'http://www.youreliteplumber.com/', 'http://bestimpressionscaterers.com/main.php', None, None, None, None, None, 'http://www.newvisionaz.org', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', None, None, 'http://larmco-oh.com', 'http://www.maisonettedistillery.ca', None, 'http://www.colonandrectalclinic.com', 'http://www.sirpizzafranklinpark.com', 'https://www.t-mobile.com/store-locator/nv/henderson/galleria-at-sunset-mall?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.dressbarn.com', 'http://www.choicehotels.com/en/choice-privileges', None, 'http://lrcorralescatering.weebly.com/', 'https://www.floxondanforth.com', None, 'https://dresspeopleltd.com/', None, 'http://Leonscaribbean.com', None, 'https://www.zippssportsgrills.com', 'http://www.clancyspubscottsdale.com/', 'http://www.alimentarimadison.com', None, None, 'http://www.atlashomeinspections.com', None, 'http://zinicolaitalian.com', 'http://www.sunsetclubcharlotte.com/', 'http://www.airspecialiste.com/', 'http://www.deltaco.com', 'http://www.wincofoods.com/', 'http://www.DFgym.com', 'https://www.smilesbysmith.com', 'http://www.drbahmanguyuron.com', 'http://salonstudiowest.com', None, '1592238192', None, 'http://royaldutchgrooming.net', 'http://www.dentistsonbloor.ca/', 'http://www.presidentspizza.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.03133.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03133', 'http://www.scottsdaledentalcare.net', None, 'http://www.nailsforyou.ca', 'http://www.zumiez.com', None, 'http://www.expressgaragedoorservice.com', 'http://acebroslv.com', 'http://www.tacarbon.com', 'https://www.onemainfinancial.com/branches/PA/Pittsburgh/15234/4721', 'http://www.starkmans.com', 'https://preciousmetalsnv.com', 'https://www.extraholidays.com/las-vegas-nevada/worldmark-las-vegas-spencer-street?lid=yelp&utm_medium=referral-affiliate&utm_source=yelp.com&Identifier=yelp&hotelid=103712&utm_campaign=localpage-worldmarklasvegas-spencer&promoid=localpage-worldmarklasvegas-spencer', None, 'https://www.lovestbrides.com', 'http://www.sakunthaionline.com/', 'http://www.gocomtrans.com', 'http://www.sanremobakery.com/', 'https://piedmontmaids.com/local-house-cleaning/nc/monroe', 'http://www.fluidmotionpgh.com', 'http://www.blisscupcakes.com/', None, 'http://www.tanprousa.com', None, 'http://www.rebekhasushi.com', 'http://www.crispfoods.com', 'http://www.usps.com', 'http://www.lvmpd.com', None, None, None, 'http://www.park2go.ca', 'http://www.horstmancomputers.com', None, 'https://www.walmart.ca/en/whitby-supercentre/3113', None, 'http://colosseumtraining.com', 'https://www.kindercare.com/our-centers/phoenix/az/000477?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=000477', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216206&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.anytimedent.com', None, 'https://www.westelm.com', 'http://www.grayhawkbeerco.com', 'http://www.nextcare.com/locations/az/phoenix-thomas/?utm_source=Yelp&utm_medium=Local&utm_campaign=phoenix_thomas', 'http://goclarendon.com/restaurant', None, None, None, 'http://www.quiktrip.com', 'http://charliepalmersteak.com/locations/las-vegas', 'https://www.sprouts.com/store/az/laveen/laveen//?utm_campaign=website&utm_medium=listing&utm_source=yelp', 'http://www.thomasharman.com?cmpid=czhr_blm_0006', None, 'https://www.autoactionaz.com/dealership-locator/locations-1909-west-van-buren-street-phoenix-az/', 'http://www.ridgecleaners.com', 'http://www.plantworks.com', '1592238330', 'http://www.powerhouseplatinum.com/', 'https://thefortunatefox.com', 'http://www.ghazale.ca/', 'http://www.outback.com/locations/nv/las-vegas-craig', None, 'http://www.boom973.com/index.aspx', 'http://www.maac.com/texas/dallas/colonial-grand-at-hebron?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://ArizonaSailingAdventures.com', None, 'https://myhearingcenters.com/locations/nevada/summerlin', None, None, 'http://www.wellerracing.com/', 'http://www.timhortons.com', 'https://local.fedex.com/nc/pineville/PNVA/?cmp=LOC-1001545-3-2-971-1110000-US-US-EN-YEXTLISTFEDEXSC', 'http://primmed.org', None, 'https://www.cleanjuice.com/menu/', 'http://www.innovativehclinic.com', 'http://www.quickchangeoil.com/', 'http://www.azmortgagebrothers.com', 'https://valleywisehealth.org/locations/community-health-center-el-mirage/', 'https://www.menswearhouse.com/store-locator/2504?utm_source=yelp&utm_medium=listing&utm_content=2504&utm_campaign=AZ', 'http://www.liveatavanteapts.com', 'https://www.staples.com', 'http://www.northamerican.com/?refcode=844-434-1236&utm_source=yelp&utm_campaign=desktop', None, 'http://99only.com/store/Las-Vegas---Beltway/', 'https://theresortatsummerlin.com/dining/casual-dining/market-place-buffet-las-vegas/', 'https://www.jph4ever.com', None, 'http://www.imsaz.com', 'http://www.afabaz.com', None, 'http://www.perfectlookhairbraiding.com', 'http://www.regissalons.com/salondetail/default.asp?salonid=448', 'http://armor-plumbing-boiler.com/index.php', 'http://www.greatwraps.com', 'http://www.steepery.com/', 'http://nailsqueentoronto.ca', None, 'http://www.rodneysbybay.com', None, None, 'http://www.fitnesspropelled.com/', 'http://www.hawksbar.com', None, None, 'http://www.shakeitupbartending.com', 'http://www.salts-of-the-earth.com', None, None, 'http://store-locator.barnesandnoble.com/store/2039', 'http://www.vbflv.org', 'http://www.outlettags.com', 'http://www.702wingspot.com/', 'http://www.kitchenconnectionllc.com', 'http://www.lvparking.com', 'http://www.radair.com/', None, None, None, 'http://magroclothing.com', 'http://www.furnituretoronto.com', None, None, 'http://www.k2elec.com/', 'http://www.delanolasvegas.com/pool/delano-beach-club.aspx', 'http://woksupreme.com/', 'http://www.markandterri.com', 'http://www.goodlifefitness.com/locations/ontario/vaughan/milani-blvd?source=yelp-websitelink-vaughanmilani-gl', 'http://www.thegreatsteak.com/stores/7525', 'http://www.newdragonexpress.com/', 'http://www.daalroti.ca/', None, None, 'http://www.yourstarpupil.com', 'https://www.mccarran.com/Fly/WhichTerminal.aspx', 'http://www.lasvegascounselingcenter.com', None, None, 'http://www.glastek.com', '1592238519', None, None, 'http://www.burlingtoncoatfactory.com', '1592238526', 'https://www.galleriamc.com', 'https://www.tcclinic.com', 'https://www.midas.com/phoenix/store.aspx?shopnum=1109&dmanum=684001', 'http://az.scottsdale.charmingcharlie.com/fashion_accessories_scottsdale_az_45.html', 'http://www.shell.com', 'http://www.lapetite.com/your-local-school/monona-wi-7148/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, 'https://www.jabzboxing.com/locations/32ndandshea/', None, 'http://www.tipsetreats.com', None, 'http://www.timhortons.com', 'http://www.amazingphotocamera.com/', None, 'http://www.waddellslonghorncorral.com/', 'http://www.desertsplashadventures.com', 'http://suburban-sanitation.com', None, None, None, 'http://www.thegilcreaseorchard.org', None, None, 'http://www.yasisplace.ca', None, 'http://philhousegrill.com', '1592238583', 'http://www.opticcreations.com/', 'http://www.trainingrevelations.com', None, 'http://www.statclinix.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, '1592238598', 'http://locations.daltile.com/az/tempe/118', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, '1592238610', 'http://www.josephsfoodandcakes.com', None, 'http://www.rowdyhair.com', 'http://www.starbucks.com/', 'http://jackastors.com/location-map/18/', None, 'https://www.choicehotels.com/ohio/wickliffe/econo-lodge-hotels/oh335/rates', None, 'http://www.blondesalon.ca', None, 'https://www.papajohns.com/international', 'http://luv2play.com/surprise/', 'http://independenceplumbing.net', 'https://pawn1st.net/our-locations/pawn1st-surprise-arizona/', None, 'http://www.lasvegasprostho.com', 'http://www.isshoniramen.com', None, 'http://www.eatatnakama.com', 'http://www.macklems.com/', '1592238663', 'http://www.towerofjewels.com/', 'https://stores.dickssportinggoods.com/oh/aurora/121/', 'http://www.lomography.ca', 'https://bostonpizza.com/fr/locations/st-bruno.html', None, 'https://www.kindercare.com/our-centers/goodyear/az/301663?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=301663', None, 'http://www.tinytooth.com', 'https://custommufflersaz.com', None, 'http://www.hairsmith.co', 'http://www.medicineshoppe.com/pharmacy-locations/pennsylvania/mt-washington/home', 'http://www.virgoesthetics.com', 'http://fawnboutique.ca/', 'http://www.btrustsupermarket.com/', None, None, 'http://www.allhoursplumbinginc.com', 'http://www.pridemgmt.com', 'https://thrifty.com/loc/ll/CA/OT/TORONTO-~-DANFORTH-(OT)/1245-DANFORTH-AVE', 'https://www.wisconsinrvworld.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.sfnevada.com?cmpid=UN7I_BLM_0006', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.shibuyala.com', 'http://www.bell.ca/internet', '1592238730', None, None, 'http://www.deltaco.com', 'http://www.pizzapizza.com', 'https://habanerofreshmex.com', 'http://www.golfanything.com', None, 'https://la-coppa.com', 'https://www.montanas.ca', '1592238753', 'https://www.rallyhouse.com/rally-house-parma', 'http://balloonscharlotte.com', 'http://tton10.wix.com/pizanocustomautobody', 'http://www.secondcup.com/location/toronto-355-danforth-avenue', 'http://www.mmpguns.com', None, 'http://www.hair-dosalon.com', 'http://www.oxfordcleanersaz.com', None, 'http://hookahlounge.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', 'http://www.silverstatevapor.com', None, 'http://www.sessionstattoo.com', '1592238788', None, None, None, 'http://wokintercuisine.com', 'http://sushi-ten.com/', None, None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=2179&localechange=1', 'http://madisoncircusspace.com', None, None, 'https://myhoneybakedstore.com/charlotte/114', 'https://wexford.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, None, None, None, 'http://www.marshallsonline.com', 'http://www.tiashortys.com', 'http://www.mariscosacapulco.org/Mariscos_Acapulco/Inicio.html', 'https://cmwireless.com', None, None, None, None, 'http://thelocalbarberandshop.com', None, 'http://www.mcgrathcpa.net', 'http://www.northranchvet.com/', 'http://www.unosalonlv.com', 'http://michelsbakerycafe.com/?q=node/1/en/', 'https://www.ebgames.ca/', 'http://www.drivesafeaz.net', 'http://www.journeys.com', 'https://www.engagestudio.com', None, 'http://www.azcostumeshop.com/', 'http://www.painsetsaveurs.com/', 'http://www.extraordinarytoys.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=12605&localechange=1', None, 'http://www.fabricland.ca', None, 'http://www.quiktrip.com/', 'http://www.ahwatukeehoa.com', None, 'http://chase.com', None, 'http://Butlerfamilydentalaz.com', None, None, 'http://www.haydenelectricinc.com', 'http://www.parmatireservice.net', 'http://www.marcos.com', None, 'https://www.eliterooterphoenix.com', None, None, 'http://www.ilovepokebar.com', 'http://sushi-mori.ca', 'https://www.propertymanagementscottsdaleaz.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.jnphoenixfamilylawyer.com', 'https://www.vans.com', 'http://www.rowefarms.ca', 'https://www.sephora.com/happening/stores/hillcrest', None, None, 'https://www.cubesmart.com/nevada-self-storage/las-vegas-self-storage/90.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'https://shakeshakeseafood.com/contact_monroe', 'http://www.montessorivisions.com', None, None, None, 'http://www.MarshProperties.com', 'http://www.setispolishboys.biz', 'http://www.ctuckerandassociates.com', 'https://www.everbrookacademy.com/our-schools/charlotte-nc-4608/?utm_campaign=enhanced-listing&utm_medium=paid-directory&utm_source=yelp', None, 'http://www.costco.ca/', 'http://www.azdermacare.com/', 'http://www.yumbudz.ca', 'https://theeggworks.com', 'http://www.forgetaboutitsupperclub.ca', 'http://www.lbcexpress.com', None, 'https://www.reflectionzdetail.com', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.lebelandcrowe.com', 'http://www.greencleanerslv.com', 'https://drgeoffreysherivf.com', 'http://www.beadworksjo.com', 'http://www.craigscustomupholstery.com', 'https://www.walmart.com/store/5066/avon-oh/details', None, None, 'http://www.philotavern.com/', 'http://www.abercrombiekids.ca/', None, 'http://www.jessieraesbbq.com', 'http://www.vetemergency.ca', 'http://www.carolinadoughnuts.com', '1592239007', 'http://www.starbucks.com', 'http://www.thespainthehollow.com/', '1592239015', 'http://www.bestclean-llc.com/', 'http://galenaeuropeanspa.com', 'https://www.kidsquest.com/location/boulder/', 'http://www.vsschnitzelhouse.com', None, None, 'http://www.fluidconcepts.net', 'https://www.myfitfoods.com/', 'http://kathysalterations.biz', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/16545+East+Palisades+Boulevard-Fountain+Hills-AZ-85268/storeid=9279?cid=ps_ylp_2020', 'http://reflectionsautodetailing.me', None, 'http://www.thecannerygrill.com', None, None, None, 'http://www.paintboy.com/', '1592239059', None, None, 'http://arizonawindowwashers.com', 'http://www.courtyardatencanto.com/', 'https://titanicaz.com', None, 'http://labayoucasino.tumblr.com/', None, 'http://www.sapporoscottsdale.com', None, None, 'http://kappatoys.com', 'http://www.shoelabworld.com', 'http://www.goodwillaz.org', 'http://bk.com/', 'http://www.soldentalaz.com', 'http://www.lasvegaskidsrkids.com', 'http://www.caninecountry.ca/', 'https://www.halibuthouse.ca/locations/halibuthouse560mulockdrive/', 'http://www.pinoyscoffeeandboba.com', 'http://cp.cuyahogacounty.us/internet/index.aspx', None, 'http://www.airdrieautotrends.com/', 'http://www.leonesflorist.com', 'http://www.wavescoffee.com', 'http://viennamarketbroadway.com', None, 'http://www.desertskysurfaces.com/', None, 'http://www.chinachilirestaurant.com', 'http://www.bethanychristianschool.org', 'http://www.mazonac.com', 'http://stores.dickssportinggoods.com/az/mesa/725/', 'http://charlottefiberglass.com', None, 'http://www.chinapalacesewickleypa.com/', 'http://www.aceaxethrowing.com', 'http://www.exlacademy.com', 'http://www.deltastore.com', 'http://www.desertsunpt.com', 'https://bloomingnails-nailsalon.business.site', 'http://www.caremd.com/', 'http://giovanniandcompany.com/', None, None, 'http://www.razzles.biz/', None, None, None, 'http://www.dollartreecanada.com', 'http://www.socialsolutionsaz.com', 'http://www.springdayspa.com', None, 'http://www.bbkingclubs.com/', 'http://haciendasolanoresort.com', 'http://www.xperiencevapes.com', 'http://www.leakpoint.com', 'https://www.abccollisionrepair.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'https://stores.loft.com/us/pa/homestead/126-west-bridge-street.html', None, None, 'http://eosfitness.com/location/tempe?utm_campaign=tempe&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', None, None, '1592239206', None, 'https://dealer.sprint.com/experts-choice', 'http://local.biglots.com/oh/stow/453', 'http://www.yayaspizza.com/', 'http://www.portioncontrolnv.com', None, '1592239219', 'http://www.usmgcorp.com', None, None, 'https://www.boydautobody.com/locations/calgary-1st-st-ab', 'http://www.tranquil-lily.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'https://www.aireserv.com/north-valley', None, 'http://www.bluerosepottery.com', None, 'https://locations.panerabread.com/oh/highland-heights/6345-wilson-mills-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://www.retroburger.ca/', 'http://crunchbistro.com', 'http://www.valuevillage.com', 'http://www.bleedingrosetattoo.com', None, None, None, 'https://www.goodyearautoservice.com/en-US/shop/AZ/Glendale/000908234-85308-2429', 'http://www.lisboabakeryanddeli.com', None, None, 'http://www.swingpgh.com/', 'http://www.daydreamsdropin.com', 'http://valleypoolcleaning.com/', None, None, 'http://www.vaultnc.com/', 'http://www.tonicsalonnv.com/', '1592239283', 'https://airpromaster.com', 'http://www.queencityautosalesnc.com', 'http://pageperpage.com', None, 'https://www.firehousesubs.com/locations/oh/willoughby-commons', '1592239298', None, 'http://laptoprepairs.com', None, None, 'http://www.lashliqueur.com', 'http://www.airportgatecafe.com/', 'http://www.naturallyyours.ca', 'http://www.shopkkbloom.com', 'http://www.honestyelectricllc.com', None, 'http://www.husd.org', 'http://www.ucalgaryrecreation.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.exacttemphvac.com', None, None, 'http://www.madisonorientalwok.com', 'http://www.crossfitarchangel.com', None, 'http://www.jolieannephotography.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://www.rockabettyssalon.com/', 'http://c2cnd.org', 'http://www.fantasticsams.com/', None, 'http://www.gamestop.com', 'https://www.safelite.com', 'http://cleanenvision.com', 'http://www.ahugheshairdesign.com', None, 'http://www.filibertos.com', 'http://www.kmjwebdesign.com', None, 'http://www.dillysdeli.com/', None, 'http://www.kimchikoreahouse.ca/', None, None, 'http://www.mississauga.ca/portal/discover/parksandgardens?paf_gear_id=9700018&itemId=300019', 'https://www.publicstorage.com/arizona/self-storage-mesa-az/85210-self-storage/787?pid=wyelp&CID=1245&CHID=AFL', '1592239382', 'http://www.teavasee.com/', 'http://www.popularpizza.ca/', None, 'http://www.steffiblackcoaching.com', 'http://www.virginiajohnson.com', 'http://www.kindercollege.ca', None, 'http://www.toysrus.com/family/index.jsp?categoryId=2255956&camp=MISC:yelp:store:page:tru:111910', 'http://www.gdpeds.com/', 'http://www.coldwaterspringsapts.com/', 'http://www.eyecarecenter.com/optometrist-locations/matthews-mint-hill-rd/?address=28105', 'http://www.minus5experience.com/', None, None, 'http://premiercleaners.com', None, 'http://www.theherbcard.com', None, None, 'http://www.maac.com/north-carolina/charlotte/post-ballantyne?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', None, None, 'https://www.unlv.edu/dental', 'https://www.thestonecollection.com/phoenix', 'http://www.sweetpetes.com', None, 'https://www.aaautocarelv.com/locations/decatur-blvd/', None, 'http://www.allnationsdriving.ca', 'http://icehousebrooklyn.com/', 'http://www.carusogourmetpizza.com/', None, None, 'http://www.sparrshspa.com', None, 'https://www.mezzo1.com/?utm_source=yelp', 'http://www.jimtuckerroofing.com', 'https://www.redmountainweightloss.com/ahwatukee/', None, 'http://www.jackinthebox.com/', None, 'http://www.thebeautyloftaz.com', 'http://www.papadelspizza.com/', 'https://www.maricopa.edu', None, None, 'https://www.lasereyecenteraz.com/eye-doctors/kianoush-kian-m-d/', 'http://www.Altus-HPO.com', 'http://yourspacesalons.ca/natural-solutions', None, None, None, 'http://www.buckle.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'https://www.glassdoctor.com/phoenix', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=1131', 'http://goodfoodmadison.com', None, None, 'http://www.suicidejims.com', None, None, 'http://www.thelaughshopcalgary.com', None, 'http://www.skyzone.com/phoenix', None, None, 'http://www.animalcareclinicinc.com/henderson-animal-hospital', None, 'http://www.center-towing.com', 'http://www.regency.edu/campus/north-olmsted-ohio.aspx', 'https://www.purdys.com/shops/details/79', 'http://www.hottopic.com', 'http://www.carolinatotalcare.com', None, 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://archstonecare.com/', 'http://www.kibosushi.com', 'http://rulysauto.com', None, 'https://www.earthfare.com/stores/', 'http://www.allapplianceneo.com', 'http://denver.unique-accounting.com', None, 'https://www.wyndhamhotels.com/hotel/33877?tel=18003291073&iata=00093785&cid=fe:di:20161220:yl:pp:dius:33877', None, 'https://vansoncuisine.ca', 'http://www.donsappliances.com', 'http://alphillipslv.com/', '1592239567', 'http://www.larrystow.com', 'https://www.marleneharriscol.com', 'http://www.consonantskincare.com', None, 'https://www.tgifridays.com/locations/1742/fridays-charlotteuniversity-north-carolina', 'https://locations.eatandys.com/ll/US/NC/Concord/8835-Christenbury-Pkwy', 'http://jmacvideo.com', 'http://www.aosmlv.com', 'http://enticare.com', 'http://www.marriott.com/hotels/travel/pitmv-springhill-suites-pittsburgh-monroeville/?scid=bb1a189a-fec3-4d19-a255-54ba596febe2', 'http://www.theciderfarm.com', 'https://www.presslyanimalhospital.net', None, 'http://www.remax.com/realestateagentoffice/lasvegas-nv-89128-sandrathomas-id11154472.html', 'http://www.meadowlarkestables.com/', 'http://www.salon-atmosphere.com/', 'http://chicagobrewinglv.com', None, None, None, 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/mississauga-2191-dundas-street-e.aspx', 'http://www.doitbest.com', 'http://sterlingssteakhouse.ca', 'http://www.saloncollage.com', 'http://www.eatatbobsdiner.com/', 'http://www.kamasutrarestaurant.ca', 'http://www.swisschalet.com', 'http://www.dunkindonuts.com', None, 'http://locations.atipt.com/grayhawk-scottsdale-az', 'http://www.magicvaporllc.com', 'http://www.starbucks.com', 'http://www.AllBreedMadison.com', 'http://www.montanameatco.com', 'http://bk.com/', 'http://www.starbucks.ca', None, 'http://www.autobell.com/ab_locations/750-n-church-st/', None, None, 'http://www.marriott.com/hotels/travel/cleta-towneplace-suites-cleveland-airport', None, None, None, 'http://workoutanytime.com/charlottewest', 'http://carolinasmiledesignsc.com', 'https://depotbarbershop.business.site/?m=true', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592239672', 'http://www.libertyiron.com', 'http://aaffordablebabysitting.com', 'http://www.quesada.ca', 'http://bk.com/', 'https://locations.theupsstore.com/wi/sun-prairie/1223-w-main-st?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.kay.com', 'https://www.ugg.com/stores/s/fashion-show-mall?latitude=36.127172&exclude=18231&page=1&longitude=-115.171661&storesPerPage=3', 'http://www.creolecajunbistro.com', None, None, None, 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpsoutheastorganic', 'http://www.wolfcamera.com', 'http://www.corygoldbergmd.com/', 'http://www.harborfreight.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.paksweets.com', 'http://www.airpads.com', None, 'http://www.norterrafamilymedicine.com', None, 'http://www.kensingtonbrewingcompany.com', 'http://25chiropractic.com/', '1592239728', 'http://coffeedaklak.com', None, None, 'http://freddyrguez.googlepages.com/', 'https://www.crossborderpickups.ca', 'http://www.dilworthbilliards.com/', None, 'http://www.ahghomewarranty.com', None, None, '1592239754', 'http://www.guggenheimhermlasvegas.org', 'http://www.pearl-factory.com', None, 'https://local.biglots.com/pa/pittsburgh/1478?zcp=pd_local_yelp', 'https://www.navyfederal.org/?cmpid=bn%7Cyelp%7Cevgrn%7Cbrn%7Cnull%7Cnull%7C01/13/2020%7Cml%7Cnull', 'http://www.sallybeauty.com', 'http://www.salonfair.com', 'https://sunvek.com', 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', 'http://www.bakersbookkeeping.com', None, 'https://phoenix.swimspas.us', None, 'http://torontopremiumoutlets.ca/outlet/toronto', 'http://www.midwifeskaleidoscope.org', 'http://www.redrockfencingcenter.com', 'http://www.azairworks.com/', 'http://auraapts.com', None, 'http://www.discountroofingnv.com', 'http://www.drvinyl.com', 'http://www.newskyrestaurant.ca', None, 'http://www.portauthority.org', 'http://www.downtownbrewfestival.com', None, 'http://www.globallylocal.ca', 'http://www.kakabeautyspa.ca', None, 'http://www.noelinwheeler.tattoo', 'http://concourseroffler.blogspot.com', 'http://www.rexall.ca/', 'http://www.trailsidetreasures.com', 'http://www.nevadatirecity.com', 'http://www.cornerstonewomenscare.com', 'http://www.easyhome.us', 'http://www.mondashaircare.com', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=1', 'http://newks.com', 'http://www.dcspoolbarriers.com', 'http://www.drrochlin.com', 'https://www.fit4less.ca/locations/alberta/calgary/408?utm_source=yelp&utm_medium=cta&utm_term=calgarymacleod-f4l', 'http://www.julietlefleur.com', 'http://www.arizonahairco.com/', 'http://www.dunkindonuts.com', 'http://montana-hookah-longue-and-smokeshop.business.site', 'http://miniso.ca', 'http://www.westairaviation.com', 'https://www.sunrisepreschools.com/locations/baseline-gilbert/?utm_source=yelp&utm_campaign=online_listing_gilbert_280&utm_medium=referral&utm_term=business_url', 'http://www.mackdentistry.com/', 'http://thayersselectmeats.com', 'http://undergrounddiesels.com', '1592239872', 'http://www.samuraicomics.com', '1592239878', 'http://www.michaelkors.com/stores/united-states/nv/las-vegas/michael-kors-palazzo', 'http://willytechshop.com', 'http://www.vernspizza.com', 'http://www.clearviewinstitute.com/', 'http://www.berkeleyplace-apts.com', '1592239893', None, None, 'https://venecia-beauty.business.site', 'http://www.haircutmenriverbendcalgaryab.ca', 'https://www.hungryhowies.com/store/hungry-howies-01805?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=01805&utm_content=Website_Link', 'https://sophiaslounge.com', 'http://www.taxicabchandler.com', 'http://www.bestchickenwings.com/', 'http://www.athletico.com/locations/tempe/?utm_campaign=yelp-listing&utm_medium=web&utm_source=yelp-tempe', 'http://www.solsticerestaurant.ca/', 'http://www.azclubluxx.com', 'http://www.sethkoreytennis.com', None, None, 'http://www.flairtrade.ca', None, None, None, 'http://www.vegasmartialarts.com', 'http://riobel.ca', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.hairea51.net', 'http://www.dmvdrop.com', 'http://carolklemp.wix.com/aefitness', 'http://www.3Brewers.ca', 'http://www.lisaturley.com', 'http://oldtownweddingcenter.com/', None, None, None, None, None, 'https://zoomrentals.com/toronto-airport-car-rentals', 'http://www.rehabplusscottsdale.com', 'http://azdirectmobility.com', 'http://www.torpedocomics.com', None, 'https://www.aladdinswindowtinting.com', None, None, 'https://www.ewingirrigation.com', None, None, None, '1592239999', 'http://www.dapaulsalon.com', None, 'http://productnightclub.com', 'http://desertmesapool.com', None, 'http://www.cltchristmasvillage.com', None, '1592240015', 'http://www.animalhospitalhighpark.com/', 'https://bhrcenter.com/location/boca-park-nv/', 'http://www.conns.com/store-locator/arizona/scottsdale-85250', None, None, None, 'http://www.bestfootspascottsdale.com/', 'http://elitepetcare.com/', 'http://www.reservesquareapts.com', 'http://www.livelovelashe.ca', 'http://www.ibrandyourbusiness.com', 'http://wingsonbroadway.com/', 'https://mugshotzofficial.wixsite.com/mugshotz', 'https://www.luckysmarket.com', 'http://linkfinancialadvisory.com', 'https://www.gocleancredit.com', 'http://www.rothmanawningco.com/', 'http://www.fredastaire.com/scottsdale', 'http://www.sweettomatoes.com', None, None, 'http://www.bellairconditioningaz.com', None, 'http://www.arbys.com', None, 'http://tempeautorepairshop.com', None, 'http://martinjlevinedds.com/', '1592240069', 'http://www.carolinaurology.com', 'http://www.whiteningxpressions.com', 'http://www.chevron.com/', None, 'http://www.jambajuice.com', 'https://www.honorhealth.com/locations/hospitals/scottsdale-thompson-peak-medical-center?utm_source=yelp&utm_medium=local&utm_campaign=Scottsdale_Thompson_Peak_Medical_Center', '1592240085', 'https://locations.wafflehouse.com/nc-pineville-1157', None, 'http://www.lasvegasapartments-r-us.com/Mirabella-Apartments-for-Rent-in-Las-Vegas.html', '1592240094', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'https://www.waterstreetpizzeria.com', 'https://familymoversexpress.com', None, None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.asphaltpavingranaldi.com', 'https://locations.jackinthebox.com/us/az/peoria/8236-w-deer-valley-rd', 'http://www.tjmaxx.com', None, None, 'http://www.swarovski.com/en-US/?utm_source=YELP&utm_medium=referral_managed&utm_campaign=YELP', 'http://www.chiefdodge.com/', 'https://www.titlenine.com/store-locator/title+nine+-+madison.do', 'http://www.tiremanusa.com/locations.aspx', None, 'http://www.wolfsonmedicalcenter.com', 'http://greenwayfamilyautoandtowing.com', 'https://www.orangetheory.com/en-us/locations/arizona/peoria/25314-n-lake-pleasant-pkwy-suite-1260/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.woodysdogbath.com', 'http://www.mayfieldbrainard.com', None, None, 'http://www.scrubsandbeyond.com', 'http://fitnessfactorycharlotte.com/', 'http://azsportsmedicine.com', 'http://www.idealservices.com', None, None, None, 'https://www.brasstapbeerbar.com/Charlotte', 'http://www.seaminglystraight.com', None, 'http://www.whitfillnursery.com', None, 'http://www.chip-n-daleslandscaping.com', 'http://www.illinitechcenter.com', None, None, 'http://www.villageicecream.com', '1592240192', None, 'http://www.carpet-cleaning-pittsburgh.com', 'http://www.thelowcarbgrocery.com', 'http://lezah.ca', 'https://www.brakesplus.com', 'http://paulmitchell.edu/phoenix', None, None, None, None, 'http://www.alohabbqgrill.com', 'https://www.esso.ca/en/gas-station/etobicoke-on-geesso-200302279', 'http://www.edencafelounge.ca', 'http://www.signsbytomorrow.com/mesa/', 'http://www.borders.com', None, None, 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://peoriafootandanklespecialists.com', None, 'http://tshirtdinervegas.com', None, None, '1592240240', 'http://lebistrodubeaujolais.com/', 'http://farmershouse.ca', 'http://www.sarkujapan.com/', None, None, 'http://www.charlotterusse.com', None, 'http://kpiteophotography.com/', 'http://www.aceshighpartyrental.com/', 'http://www.harveys.ca', 'https://www.walgreens.com/locator/walgreens-11001+s+eastern+ave-henderson-nv-89052/id=6545', 'https://www.altimadental.com/locations/first-canadian-place', 'http://www.rockcitytaphouse.com', 'http://www.thelucky20cafe.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCSC', None, None, 'https://www.yeahyeahspizza.com/toronto', None, 'https://locations.panerabread.com/oh/parma/8109-w-ridgewood-dr.html', 'http://www.clearsound.co', 'http://www.sunrisecoffeelv.com', 'http://www.herbergertheater.org', None, None, 'https://pittsburghmoving.net', 'http://www.phoenixcakecompany.com', 'http://www.timothys.ca', 'http://www.olivetree-apartments.com', None, None, 'http://www.ltayh.com', 'https://www.walgreens.com/locator/walgreens-1745+e+southern+ave-tempe-az-85282/id=1197', 'http://dobsonranchdentalcare.com', None, 'http://www.elitedancestudiolv.com', 'http://www.boosterjuice.com', 'http://www.meckabc.com', 'https://www.realestatelawfirmphoenix.com', '1592240325', 'http://www.goodyearsfamilymedicine.com', 'http://www.drdanstrinkoski.com', 'https://www.petpeoplestores.com/avon-store.html', 'http://www.bedfordautocare.com', 'http://www.shininghopefarms.org/', None, 'http://www.freshandeasy.com/', 'http://www.csuohio.edu/artgallery', 'http://www.desertpalettepainting.com/', 'http://www.premierairsolutions.com', '1592240349', 'http://www.desertroselandscaping.com', '1592240354', 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.dmconcrete.biz', 'http://bluestardiner.ca/', None, 'https://sweetiepiescatering.com', 'https://www.azbouncepro.com', 'http://www.ritters.com', None, 'http://Arizonasoldsisters.com', 'http://www.restaurantdepot.com', 'http://pizzafire.com', 'https://www.ikea.com/us/en/stores/tempe/', None, 'http://www.regaloaksdental.com/', 'https://www.signaturestyle.com/locations/pa/penn-hills/borics-hair-care-penn-hills-shopping-center-haircuts-75141.html', 'http://99only.com/store/Las-Vegas---Beltway/', None, 'https://www.jovannalv.com', 'http://www.coppercanyondentalaz.com/', '1592240397', 'http://journeyeducation.org', None, 'http://www.tandyleatherfactory.com', None, None, None, 'https://local.fedex.com/nv/las-vegas/office-1441/', 'http://www.madameboeuf.com', 'https://www.fitzroyrentals.com', 'http://www.resumetarget.ca/location/ontario-on/toronto/', '1592240420', 'http://callnoworriesjanitorial.com', 'https://www.autozone.com/locations/in/avon/7474-e-us-36.html', None, 'https://www.zoup.com', 'http://www.thedistrictatgvr.com/alsGarage.php', 'http://www.kixs.ca', 'http://www.immigroup.com', 'http://www.burlingtoncoatfactory.com', None, None, None, 'http://www.swensensaz.com', None, 'http://www.arrowheadautocare.com', None, 'http://www.lucasautomotive.ca/', 'http://lululemon.com/toronto/queenstreet?cid=yelp', None, 'https://www.nothingbundtcakes.com/bakery/az/surprise?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=surprise_300', None, 'http://www.rnbflooring.com', 'http://www.fortpittblockhouse.com/', 'https://www.hilton.com/en/hotels/cltbahw-homewood-suites-charlotte-ballantyne-nc/?SEO_id=YELP-HW-CLTBAHW', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.cortebellagolfclub.com', 'http://www.popsbarber.com', None, '1592240482', None, 'http://www.greenbeauty.ca', 'http://24hrlockoutsmadison.com/', 'https://kevindeon777.wixsite.com/remodel', 'https://www.needforsweetslv.com', 'http://suzieqluxe.com', None, 'http://www.torontoislandsup.com', None, 'http://www.azhumane.org', 'http://www.providenceprepschool.com/', '1592240510', 'http://kierlandresort.com/fine-dining-at-scottsdale-restaurants/scotch-library/', 'http://www.vocellipizza.com/mccandless_pa', 'http://shawarmaroyale.com', 'http://bullseyervrepair.com', None, None, 'https://www.westelm.com/stores/ca/on/toronto-shops-at-king-liberty/', 'http://www.sterlescountryhouse.com', 'http://www.dawgdayzcare.com/', 'http://www.superiortire.ca/locations/mode/4/3-laidlaw-blvd-markham-on-l3p1w5.aspx', 'https://experigreen.com/service-area/charlotte-nc/', 'http://www.michaelscateringevents.com', 'http://www.footdocvegas.com', 'http://www.InfinityAcuAZ.com', 'http://www.eggsmart.ca', 'http://www.cakestoyou.net', None, None, None, 'http://www.thecorneralley.com', 'http://www.pinkpetalsflorist.com', 'http://www.thecroftdowntown.com/', 'http://www.dbacks.com/', 'https://www.smilefitnessdentalcenter.com', 'https://stores.savers.com/nv/lasvegas/savers-thrift-store-1047.html', 'https://www.appliancepartscompany.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTWS', None, 'http://www.MortgageAssociatesOntario.com', None, 'https://locations.rallys.com/oh/parma/6201-brookpark-road/?utm_source=Yelp', None, 'https://www.bestbuysoccer.com', 'http://www.aeropostale.com', 'http://www.alternativehealingconnection.com/', None, 'http://www.mastercleaningaz.com', 'http://www.thepoddrop.com', 'http://www.dozoaz.com/', 'http://luckysloungelv.com', 'http://www3.hilton.com/en/hotels/north-carolina/hilton-charlotte-center-city-CLTHHHF/index.html', 'http://bestofsevenbarbers.com/', 'http://www.lorispetagree.com', 'https://deltaco.com', 'http://firstwindfitness.com', 'https://lakehealth.org/Locations/TriPoint-Medical-Center', None, 'http://www.swisschalet.com', None, None, None, None, '1592240633', 'http://www.midaslocator.com/AutoRepairFinder/tabid/151/Default.aspx', 'http://www.pricklypeachwaxbar.com', None, 'http://asappoollv.com', 'http://www.snipits.com/locations/avon/', 'http://www.timhortons.com/', 'http://www.43north.biz', 'http://www.mixxmethod.com', 'http://www.rizegaragedoor.com', None, 'http://www.papagostables.com', None, None, None, 'http://theswedishconnection.net', 'https://www.bestwestern.com/en_US/book/hotel-rooms.66083.html?iata=00171890&ssob=BLBWI0003G&cid=BLBWI0003G:yext:website:66083', 'http://federicosmexicanfood.com', None, None, 'http://www.calvarychristiandaycare.com/', 'http://www.phxdj.com', None, 'https://www.ezwindowsolutions.com/cleveland/', 'http://www.mrappliance.com/pittsburgh', None, 'http://www.opsiseyecare.com', 'http://www.avanteoptics.com', None, 'https://www.chronicinktattoo.com/locations/tattoo-shop/chronic-ink-midtown-toronto-yonge-eglinton/', None, 'http://www.adaptiveforce.com', None, 'http://www.thecatnfiddlepub.com', 'http://www.valleyymca.org', 'http://www.ladybugpestcontrol.com/', None, None, '1592240712', None, 'http://www.greenfieldcitrus.com', 'http://www.prada.com', None, None, None, 'http://www.towncentredentalclinic.ca', 'http://www.hobbyhobby.com', None, 'https://southpointcasino.com/entertainment/grandview-lounge/?cid=ypgl', 'http://crystalclearreflectionsaz.com', 'http://danielacaltarumd.com/', None, 'http://www.cleantheworld.org/', 'https://www.famousfootwear.com/?partnerid=YELP', 'http://www.newhorizonlittlelearners.com', 'https://www.hairclub.com/locations/nv/las-vegas/hair-loss-clinic-292/?pub=loclisting&utm_source=yext&utm_medium=loclisting&utm_campaign=YX_292', 'http://galatimarketfresh.com', '1592240751', None, 'http://www.toysrus.ca', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/9302+Olde+Eight+Road-Northfield+Center-OH-44067/storeid=4301?cid=ps_ylp_2020', None, 'http://www.salonritualsaveda.com', 'http://www.jetfuelcoffee.com', None, 'http://www.mrhero.com', 'http://www.lululemon.com/thornhill/promenade?cid=yelp', 'http://www.destinationweddingphotographycalgary.com', 'http://www.golfthebridges.com/barandgrill/', '1592240777', 'http://funtropolis.ca', 'http://www.bilmarcompanies.com', None, 'https://www.aznaturalselections.com', 'http://locksmith4Uvegas.com', 'http://scotiaplaza.kidsandcompany.com', None, '1592240796', 'http://www.greatclips.com', 'http://gremassagetherapy.com', 'http://www.fortunenails.ca', 'https://locations.massageenvy.com/arizona/peoria/10006-w-happy-valley-parkway.html', 'https://www.extraspace.com/storage/facilities/us/north_carolina/charlotte/1000000404/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.kodisnaturalpetfoods.com', None, 'https://www.papamurphys.com/store-finder/position?utm_source=yelp&utm_medium=2018ads&utm_campaign=SC011', 'http://www.arizonahairco.com', None, None, 'http://www.desi.bar', None, 'http://mkt.com/mobile-bubbles', 'https://www.walmart.com/store/3473/las-vegas-nv/whats-new', None, 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'http://www.waborasushi.com/', 'http://salon7000.com/', None, None, 'http://www.whitecastle.com', None, None, None, '1592240855', None, None, '1592240862', None, None, 'http://www.averyonthegreen.com', None, 'https://www.southviewdentallv.com/index.php', None, None, 'http://www.firstcu.net', 'http://www.anytimegaragedoor.com/', 'https://sardellaspizza.com', None, 'http://www.panevinorestaurant.net/about.html', 'http://www.newhealthdentalaz.com/', None, 'http://www.hatleystore.com', 'http://xtremeairaz.com', 'https://www.phoenixconventioncenter.com/orpheum-theatre', None, 'http://www.veronadentalcare.com', 'http://www.canyonridge.org', 'http://mint-landscape-creations-llc.business.site', None, None, 'http://www.academyofsound.org', None, 'http://lowell.wisc.edu', None, None, 'http://www.chandlervisioncenter.com', None, 'http://www.sugarmarmalade.com', 'http://shoparooni.com', 'http://www.dieselbarbershop.com', 'http://www.allcitytransportation.com', None, 'http://premierdental702.com', 'http://www.dominos.com', 'http://www.lazylizardaz.com/', 'http://www.qqteaplus.com', 'http://snailmotorsports.com/', 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'http://www.lacasalatina.net', 'http://www.itzzapizza.com', 'https://www.aritzia.com/en/store-locator?q=M9C+1B8&view=results', 'https://www.plannedparenthood.org/health-center/wisconsin/madison/53713/madison-south-health-center-3937-91860?utm_campaign=madison-south-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', None, None, 'http://www.azkarateacademy.com', 'http://olivebranch412.com', None, None, 'http://susiesestateaz.com/estate_sales', None, None, 'http://www.thaiexpress.ca', 'https://www.advantagestorage.net/self-storage/az/phoenix/advantage-storage-moon-valley/', 'https://florist.1800flowers.com/us-nv/1-800-flowers-shoppe-las-vegas', 'http://www.weavebaratl.com', 'http://www.migrationlaw.com', 'http://www.iceburghs.com', 'http://www.drgreencerts.com', 'http://modernnailsandlash.com', 'https://recreationalartstudio.com', None, 'http://design-ramon.com', 'http://www.sallybeauty.com', 'http://www.just4funsportingclub.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=1378&utm_content=bpas', 'http://www.lush.ca', None, 'http://www.madsens.ca/', 'http://www.sportracks.com', None, 'https://www.fatburger.com/locations/rancho', 'http://www.azsuperiorhomeinspections.com', 'http://www.earnhardtcadillac.com/', None, '1592241033', 'http://barneyslounge.ga', 'http://brianwilliamsdds.com/', 'http://www.simplyflowerstoronto.com', None, 'http://www.arizonaautowashscottsdale.com', 'http://www.dunkindonuts.com', 'http://www.PattersonHomesAZ.com', None, 'http://www.outback.com/locations/oh/independence', 'https://pablocanada.com', None, 'http://www.mychiropractoraz.com', 'http://www.hollospapercraft.net/', 'https://www.searsauto.com/stores/6601?psid=campaigncode-6601', 'http://www.sayyestoherdress.com', None, 'http://www.eyestudio.ca', 'http://www.highlandfarms.ca', 'https://tendollarshirtstore.com', 'http://www.cineplex.com/Theatre/cineplex-odeon-eglinton-town-centre-cinemas', 'http://www.myhusky.ca/station_locator.html?provinceID=AB', 'http://peaksandrafters.com', 'http://www.junkmastersinc.com', None, 'https://www.filerchiropracticpittsburgh.com', 'http://www.westsidemarket.org/vendor.aspx?id=77', 'http://www.ttc.ca/Subway/Stations/St_Patrick/station.jsp', 'http://www.gzcomics.com/locale.html', 'http://www.deltaco.com', 'https://jade-chinese-kitchen.business.site', None, 'http://www.bojangles.com', 'http://Clocktowerbar.ca', 'http://valleyislepumping.com/', 'http://www.quiznos.ca', None, None, None, 'http://www.bigotires.com', None, 'http://stpaulpgh.org', 'http://coopersbbqco.com/', 'http://www.ecokingaz.com', None, None, 'http://www.powervac.ca/power-vac-toronto-gta', None, 'http://www.myphoenixair.com', 'https://www.gianteagle.com/Stores/Store/?storeId=6299', 'http://www.Team1stRealEstate.com', 'http://www.fickleonline.com', 'https://vcahospitals.com/bakerstown?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Bakerstown_Animal_Hospital=main_url', 'http://www.jglennhome.com', '1592241164', '1592241167', 'https://www.doggiedistrictaz.com?utm_source=yelp&utm_medium=social', None, None, 'http://changjiangbestmadison.com', 'https://www.theacteam.com', None, 'http://www.eatoooweebbq.com', 'http://fourcornersbakery.com', None, 'http://www.paintstoretoronto.com', 'https://stores.toysrus.com/az/goodyear/baby-store-goodyear-az-b5641.html', 'https://www.fiix.io', 'http://www.visualharmonyphotography.com/', 'https://landmarkautoanddiesel.com', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=830', 'https://finedetails.ca', 'http://www.tbdc.com', 'https://www.liveedgelust.com', 'https://www.kinjosushiandgrill.com', 'http://GrizzlyAC.com', 'http://www.opticausa.com', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___sun_city_peoria', 'http://www.advancedhearinggroup.com', 'https://sacredpi.com', None, 'https://www.transformyourself.ca', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282967270&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'https://arirangkoreanbbq.business.site', 'http://www.marqueetheatreaz.com', None, 'http://peoriaartisanbrewing.com/tap-room/', 'http://www.holeechow.com', 'https://www.abcgaragedoor.biz', 'http://webersvintageicecream.com', None, 'http://www.leewiyoga.com', None, 'http://www.lucapizza.ca/', None, 'https://www.wangskitchenpa.com', 'http://northofbombay.com', 'http://www.eandrsweetery.com', 'http://indodesignerrugs.com', 'http://www.landmarkhomeserv.com', None, None, 'http://www.saharaautolv.com', 'http://www.drlizcruz.com', 'https://www.wingstop.com/location/wingstop-230-glendale-az-85306/menu', 'http://www.northcoastjawcenter.com', None, '1592241292', None, 'https://www.loblaws.ca/store-locator/Loblaws+-+St.+Clair+Ave+West/1212?storeId=1212', None, 'http://glassking.com', None, 'http://www.glamoursalonandspa.ca', None, 'http://www.CapstoneBrokerage.com', 'http://www.myrivertowne.com', 'http://www.hotrodpiercingcompany.com/index.html', 'http://www.tuckyshotdogs.com', None, 'http://www.getdynamicdetailing.com', None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/20/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://local.tiresplus.com/store/Madison-East?lw_cmp=YLP_TP_53714&utm_source=YLP&utm_medium=TP_53714', None, 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', None, 'http://www.theyardpgh.com/market-square', None, None, None, 'http://www.nissanairport.com', 'http://pilateselementlv.com', 'http://bodega13.com/', 'http://freedomclothingcollective.com', 'http://trackofficefurniture.com/', None, 'https://locations.visionworks.com/ll/US/PA/Pittsburgh/120-Fifth-Ave-Pl', 'http://www.healthree.ca', None, None, '1592241373', 'http://www.glamourco.com', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', 'http://www.rei.com/stores/paradise-valley.html', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.cornerstone-familypractice.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, None, 'http://www.fitkitchen.ca', 'https://www.mastercuts.com/locations/nv/henderson/mastercuts-galleria-at-sunset-haircuts-3331.html', 'https://locations.wendys.com/united-states/pa/mcmurray/3500-washington-rd', 'http://www.mccormickandschmicks.com/Locations/pittsburgh-pennsylvania/pittsburgh-pennsylvania/FifthAve.aspx', 'https://www.strongsville.org/departments/parks-recreation', None, 'http://www.ppcp.org', None, '1592241411', None, 'http://www.allcomfortservices.com/', 'http://www.eliteautoaz.com', 'http://www.stacysplacescottsdale.com', 'http://ductmanofnevada.com', 'http://www.compolastastypizza.com', None, 'http://www.brighton.com', 'http://www.maclinford.com', None, 'http://www.regalcarpetcleaners.com', None, 'https://mrjims.pizza/149.cfm', 'http://www.amberoaksrestaurant.com/', None, None, 'http://www.birkdaledental.com', 'https://www.fastmed.com/urgent-care-centers/chandler-az-walk-in-clinic-west-ray-road/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', None, 'http://www.levelsfitness.net', 'http://www.borealis-salon.com', 'https://www.nickandmikebarandgrill.com', 'http://uniongrilltap.com', 'http://lululemon.com', None, 'http://www.pacificfitnesslv.com/', 'http://hairbyhall.schedulista.com', 'http://www.kierlandresort.com/dining/nellie-cashmans/', 'http://denierlaundromat.findalaundry.org', None, 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpnortheastorganic', 'http://www.myvalleyagent.com', 'http://www.littleotterswim.com', None, None, 'http://www.peoriakayakrental.com', 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://www.kingwestvets.com', None, 'http://www.pointerscrapbooking.com/', 'http://www.cocktailemporium.com', None, 'http://www.nyahsmobilegrooming.com', None, 'http://www.gaetanosmayfield.com/', 'http://www.pool-mart.ca', None, 'http://tullys2.com/', 'https://www.signatureplasticsurgery.net', 'http://www.spinink.ca', 'http://www.wildhorsepassresort.com/kosin', 'http://sol-nails-spa.business.site', 'https://pandalibre.com', None, 'http://www.awaxmanlaw.ca/', None, 'http://www.nellisasc.com', 'https://shop.nordstrom.com/st/last-chance-clearance-store?cm_mmc=yelp-_-ycm-_-rack-_-780', None, None, 'https://www.canadianair.info', 'http://toothfairychildrensdental.com', None, None, None, 'http://www.handandstone.ca/locations/bloor-west', None, None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.europeanlv.com', 'http://www.priorityhealthgroup.vegas', 'http://www.freewayinsurance.com', 'https://locations.wendys.com/united-states/oh/stow/1051-w.-graham-street', 'http://www.foodlion.com', 'http://www.joedufek.com?cmpid=CKMF_BLM_0006', 'https://www.orleanscasino.com/dine/casual-dining/medley-buffet?disid=wmm_yelp_to_corporate_medley_organiclink', 'https://phoenixtrimatree.com', 'http://www.greenmangopest.com', 'https://locations.sonicdrivein.com/az/glendale/13751-west-glendale-avenue.html', 'https://www.kindercare.com/our-centers/mesa/az/301365?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=301365', None, 'http://www.sweetmangoohio.com', 'http://www.kfc.com', None, 'http://www.altfitpilates.com', 'http://www.nakedmagicians.com', None, 'http://prestocalzonebakery.com', 'http://www.starnail.com/', '1592241614', 'http://serenityhospiceaz.com/home/1792243', 'http://www.vans.com', 'http://familysqueezedlemonade.com/', 'http://codyscavecreek.com/', None, 'http://www.dwcpinc.com', 'http://www.glendaleazsda.org/', 'http://www.timhortons.com', 'http://www.bankofamerica.com', None, None, 'http://spa4pawsaz.com', 'http://www.turnhousegrille.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=2486&localechange=1', 'http://encompasshealth.com/desertcanyonrehab', 'http://www.doc4women.com', 'https://www.bloomingdaysfloral.com', 'http://www.maddissouthernbistro.com/', None, 'http://www.cabcpr.com', 'http://www.upcinematics.com', 'http://drjazzdetailing.com', 'http://www.thedogstop.net/', 'http://www.azbone.com', 'http://www.cleatswings.com', 'http://loparos.localmobil.com/', 'http://www.scottsdale-dentistry.com/index.php', 'http://treasureisland.com/restaurant/17/the-coffee-shop', None, 'http://www.adelaidehallto.com', None, 'http://www.vantagehotels.com/hotel-details.cfm?idp=30026', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, 'http://www.einsteinbros.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://stores.jcpenney.com/nv/lasvegas/clothing-stores-lasvegas-nv-2848.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2848', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.fineartspermanentcosmetics.com', None, 'http://www.zyng.com', 'https://www.downeastbasics.com', None, '1592241718', 'http://www.enlightanspraytan.com', None, None, None, 'http://paparocks.com/', 'https://www.wyndhamhotels.com/hotel/13899?tel=18002521709&iata=00093785&cid=fe:ra:20161215:yl:pp:ramus:13899', 'http://qnailscottsdale.com/', 'http://www.economytowinglv.com', None, None, None, 'http://www.centrestauto.ca', None, 'https://www.NEXAMortgage.com', 'http://www.presstalent.com', 'http://www.k9couture.ca', None, 'https://www.sleepcountry.ca', None, 'http://joynailsspa.business.site', None, 'http://www.mipueblo.us', '1592241770', 'http://www.cafe-mirage.com', 'http://www.sammyspizza.com/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://undergroundbutcher.com', 'https://stores.chicos.com/s/chico-s-the-district-at-green-valley-ranch', None, 'http://www.diamondloungeaz.com/', 'http://www.marcs.com/stores/marc-s-willowick-grocery-store-44095.aspx', 'http://www.boosterjuice.com/', 'http://www.smoothieking.com', 'http://www.mensclothingaz.com', None, 'http://thebodyshopgilbert.com', 'http://www.mark-taylor.com/arizona/san-hacienda/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.amfamilyspine.com', None, 'http://www.clarkcountynv.gov/vote', None, 'https://www.gianteagle.com/Stores/Store/?storeId=440', 'http://www.ocarizona.com', 'http://www.citynationalarenavegas.com', 'http://www.accesshealthdental.com', None, None, None, 'http://www.amscharters.org/peoria', 'http://www.oldchicago.com/mesa-superstition-springs', None, None, 'https://thrifty.com/loc/ll/US/AZ/PHOENIX-AP/1805-E-SKY-HARBOR-CIRCLE-SOUTH', 'http://www.celebritypatios.com/', 'https://www.walmart.com/store/1464/charlotte-nc/whats-new', 'http://www.arizonafireplaces.com', None, 'http://www.calvarycenter.com', 'http://www.bigabaldis.com/', 'http://www.bigplusfashions.com/', 'http://www.shampoochdogspaw.com', None, 'http://lowestpricedepot.com', None, None, 'https://www.shortrunprintingltd.com/Quote/index.php', 'http://www.palazzo.com/', 'http://superiorplumber.ca', 'http://www.chambersobgynlv.com', 'http://stanleysteemer.com', 'https://www.laytondentistrync.com', 'https://www.sonoraquest.com/find-a-location/scottsdale-scottsdale-rd-mescal/', 'https://buffetmandarin.weebly.com', 'http://www.americandrain.com', 'http://www.realfruitbubbletea.com', 'https://www.PUREfectReflection.com', None, 'https://www.telus.com', 'http://millermassage.com', 'http://www.weststar.org/pages/about/b_sunset.html', None, 'http://shanghai1938.biz', 'http://www.qualitycleanohio.com', 'http://www.silverstatedental.com', '1592241931', 'https://www.eddiev.com/locations/nc/charlotte/charlotte/8521?cmpid=br:ev_ag:ie_ch:dry_ca:EVQ420LOCURL_dt:20200511_sn:yelp_gt:charlotte-nc-8521_pl:locurl_rd:1019', None, '1592241939', None, 'http://desertwindawards.com', None, None, 'http://mintlounge.ca', 'http://dsw.townshoes.ca', None, None, None, 'http://www.peterpiperpizza.com/', None, None, 'http://shawbuttebarbershop.com/', 'http://www.christopherspub.net', 'http://locations.arbys.com/us/wi/sun-prairie/829-bunny-trail.html', 'http://www.mysweetblessingsbakery.com', 'http://kaizokupokebowl.com', None, None, 'http://www.coveralllasvegas.com', 'https://mikeshaulingservices.com', None, 'http://www.5rchathai.com', 'http://www.pittsburghplayhouse.com', None, 'http://stapleygaragedoor.com', 'http://www.mbco.ca/', 'http://www.union.wisc.edu/', 'http://www.icedenscottsdale.com', 'http://www.sunchain.com', None, 'http://www.laylaspalace.com', '1592242020', None, 'http://www.ackermanhomeinspections.com/', 'http://www.mysisterscloset.com/', None, 'http://www.big5sportinggoods.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.indacutbarbershop.com/', None, 'http://www.monkeesofcharlotte.com', 'http://www.financeofamerica.com/jrencher', 'http://www.littlecaesars.com/Locations/tabid/92/directions/85240/Default.aspx?id=MTUxNTAwMDQ%3d', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', None, 'https://www.reginellapizzeria.com', 'http://www.eastsidemarios.com', 'http://www.pittsburghcyclecenter.com', None, None, 'http://www.fleetfeetcleveland.com', None, 'https://www.brightnow.com/dentist-near-me/chandler-dentist/40050?utm_campaign=local_profiles&utm_medium=profiles&utm_source=yelp', 'http://www.securitydatadestruction.com', 'http://www.innovativehealinglv.com', 'http://www.urbandog.ca', 'https://woodiesautoservice.com', 'https://www.scene75.com/cleveland/eat-drink/food-truck-alley/', 'http://massagemaniaglendale.com', 'http://www.bottleshop48.com', 'http://www.chrislopez.net?cmpid=H3LE_BLM_0006', 'http://www.dunkindonuts.com', 'http://a-zhandymanservicesllc.com', 'https://www.faucetdoctorplumbingaz.com', 'http://signaturenevada.com', None, 'http://www.msfstrong.com/', 'http://www.parkbluesky.com', 'http://www.TheSchielkeGroup.com', None, 'http://www.motel6.com/reservations/motel_detail.aspx?num=2012', 'https://www.simondentalcare.com', 'http://sandblastinglasvegas.com', 'http://www.thegreatsteak.com', 'http://www.linsasianfusion.com', 'http://www.rubinsfurniture.com', None, 'http://www.hairstory.ca', None, 'http://www.abcfest.com', 'http://www.mybenzparts.com/', None, 'http://www.MariachiColonial.com', None, 'http://www.marbleslab.ca', 'http://www.lushfloral.com', 'http://www.llcrv.com/', 'https://madisonsbarandgrill.netwaiter.com/monroeville', 'http://www.ogradysoncollege.com', '1592242202', 'http://www.4naturesfinest.com', 'http://marcellopointeclaire.com', None, 'http://www.barargon.com', None, None, 'https://bodybeautifullasermedi-spa.com/locations-near-me/laser-hair-removal-bethel-park/', 'http://www.footlocker.com', 'http://www.daverubinsonpools.com', 'https://www.decathlon.ca/fr/c/135-decathlon-brossard', 'http://spicnspanspotlesscleaning.webs.com', None, 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.rowefarms.ca', 'http://www.spectaclelovesyou.com', 'http://www.boasteak.com/balboa', 'http://hawgndawgexpress.com', None, None, 'http://sfsourdougheatery.com/', 'http://foosing.weebly.com', None, 'http://www.encorecleveland.com/', 'https://www.joysquad.com/locations/las-vegas-photo-booth-rental', None, None, 'http://chase.com', 'http://www.ginzacuisine.ca', '1592242278', None, 'http://www.peaksathleticclub.com', 'https://www.hilton.com/en/hotels/phxsaht-home2-suites-phoenix-airport-south/?SEO_id=YELP-HT-PHXSAHT', 'http://southpointcasino.com/dining/coronado-cafe?cid=ypcor', 'https://www.cash1loans.com/locations/arizona/phoenix-thomas.aspx', 'http://www.co-operateon.com', None, '1592242301', None, None, 'http://www.mossgardenhome.com', 'http://www.amazingyoga.net/', 'https://br.coffee', None, 'http://nikisplace.com/', 'https://www.smartstyle.com/en-us/locations/nv/las-vegas/located-inside-walmart-3473-haircuts-3334.html', None, 'https://everythingbilliards.net', 'http://www.unionhairparlor.com', 'http://www.eastsidemarios.com/locations/newmarket/ontario/newmarket/', 'http://azurogyn.com/arizona-urogynecology-scottsdale', 'http://www.luke.af.mil', 'http://xoliquorlasvegas.com', None, None, None, None, 'http://www.nathansstoneworld.com', 'http://www.sheratonmesa.com/restaurants-in-mesa-az', None, 'http://www.jilliansbride.com', None, None, 'http://www.beautif-eyestudios.com', None, 'http://509cafe.com', 'https://www.aqualityrefrigeration.com', 'http://www.galeriesdessources.com/fr/', 'http://AccuProINSPECT.com', None, 'http://www.treichels.com', None, 'http://pupscoutsdogtraining.com', None, None, 'https://thymextable.com', 'http://agency.nationwide.com/agent/bill-buchanan-320013227-32001322700000', None, None, None, None, 'http://www.granitebistro.com', None, 'http://www.VegasHypnotherapy.com', 'https://plan.dignitymemorial.com/yp/plan/?id=483326102&utm_source=yp.com&utm_campaign=ypm&utm_medium=display&utm_term=507&utm_content=mlp', None, None, None, 'http://www.caremore.com', 'http://www.tomsitaliantuneandservice.com/index.html', 'http://hairinthecitycharlotte.com', None, 'http://www.themillstaphouse.com', 'http://www.ihg.com/candlewood/hotels/us/en/phoenix/phxbc/hoteldetail', 'https://www.dillards.com/stores/arrowhead-towne-center-glendale-arizona/0907', 'http://www.mrpita.com/sitecharlotte.html', 'http://www.thelvh.com/calendar/12-nunsense', None, None, None, None, 'http://www.shopkla.com', 'http://matthewsalterationsandcleaners.com', None, 'http://www.blindstogo.com/en/stores/richmond-hill?ua=Richmond+Hill%2C+ON+L4C+3B6%2C+Canada&rds=25', None, 'http://www.rebeloil.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3352+Kent+Road-Stow-OH-44224/storeid=3360?cid=ps_ylp_2020', 'https://toddsbathtubs.com', None, None, 'http://Sachisalon.Com/', None, None, 'http://www.kaffeeklatsch.ca', None, None, 'https://my.clevelandclinic.org/locations_directions/regional-locations/medina-mob', 'http://www.classictan.biz', 'https://petermanlumber.com', 'https://storexpressselfstorage.com/etna/units', 'http://www.banfield.com/veterinarians/sc/rock-hill/roc?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://uptown550.com', 'http://www.epicentretheaters.com/', 'http://www.gotammollc.com/', 'http://www.aestheticpittsburgh.com', None, None, None, None, 'http://www.southsidepittsburghbarbershop.com', 'http://www.rebelpools.com/', 'http://www.rosedaledentalcentre.ca', None, None, 'https://exclusiveengines.wixsite.com/exclusiveengines', 'https://www.summerlin.com/downtown-summerlin/overview.html', None, 'http://stemspa.com', '1592269454', 'http://www.northlandkia.ca', None, None, 'http://nebulanails.com/', 'http://goldenvalleymesa.com', 'http://bestpetgroomingmesa.com', None, 'https://pizza.dominos.com/illinois/urbana/1108-n-cunningham-ave/', None, 'http://www.mrhero.com', '1592269475', None, 'http://www.cineplex.com/Theatres/TheatreDetails/Scotiabank-Theatre-Chinook.aspx', None, 'http://www.tacotontos.com', 'https://www.choicehotels.com/arizona/phoenix/rodeway-inn-hotels/az244?pmf=yelp&mc=blypypaf', 'https://www.signaturestyle.com/locations/pa/penn-hills/borics-hair-care-penn-hills-shopping-center-haircuts-75141.html', 'https://www.nothingbundtcakes.com/bakery/pa/upper-st-clair?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=upper-st-clair_238', 'http://www.americaneyeglassrepair.com/', 'http://www.chalks.ca', None, None, None, None, None, 'http://www.a-burrito.com', 'http://www.rocknes.com', 'http://www.gobelievesushi.com/', None, None, None, None, 'http://www.pricechopper.ca/', None, 'http://www.timhortons.com/ca/en', None, None, 'https://www.hooters.com/locations/1080-champaign', None, 'http://www.swvets.com', None, 'http://snsrx.com', None, 'https://www.VegasMeansBusiness.com', None, 'http://www.shell.us', None, 'http://neondesertdjs.wix.com/home', 'http://www.bruceparkerdmd.com/', None, 'https://www.uptownsmilesaz.com', 'http://Lamexicanacantina.com', None, 'http://www.findinghomesinhenderson.com', 'https://www.walgreens.com/locator/walgreens-1902+w+franklin+blvd-gastonia-nc-28052/id=5877', 'http://www.cookiecrumblecafe.ca', None, None, 'http://matthewsanimalclinic.com', 'http://www.elimotors.ca', 'http://www.kutychiropractic.com', None, None, 'http://tattoofactoryofgastonia.com', 'http://www.casaramosmesa.com', 'https://u-stor.com/locations/arizona/bell/', None, 'http://www.casalinochiro.com/', 'http://bottledandtapped.com', 'http://www.tesoroscottsdale.com/', None, 'http://www.procclv.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=yelp', 'http://www.chapmanvaluecenter.com/', 'https://taffiebuccilcsw.com', 'https://landmarkrealtyllc.managebuilding.com', 'http://www.pizzaFive85.com', 'http://www.dollartree.com', 'http://ironbutterflypilates.com/', None, None, None, None, 'http://www.GigisCupcakesUSA.com/', 'http://www.nfclean702.com', 'http://www.braddockcarnegielibrary.org/', 'http://www.strongstyle.com/', 'http://lacarnita.com/', 'http://Rubinovs.com', None, None, None, 'https://www.taylormorrison.com', None, None, None, None, 'http://www.tropicalsmoothiecafe.com', None, 'https://ashleyhomestore.ca/pages/vaughan', None, 'http://www.wimpysdiner.net', None, 'http://www.cinnabon.com/', None, None, 'http://www.drewmenas.com', None, None, 'https://www.americanstandardair.com/how-to-buy/find-your-dealer.html', 'http://www.londonbarbers.ca', 'http://www.crossfit416.ca', None, 'http://www.happyalldaybreakfast.com', 'https://extremepita.com', 'http://www.levinfurniture.com', 'http://www.cbunited.com/susanchambers', None, None, None, None, None, None, None, 'http://www.chinachinamesa.com/', None, 'http://www.thegreatergoodbar.com', 'https://www.calgarymeats.com', None, 'http://www.thesakeexpress.com', None, None, 'http://www.rebeloil.com', None, None, None, None, 'http://splashville.ca', None, 'http://www.hickoryridgemovies.com', 'http://www.questrade.com', None, 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', None, 'http://stitchit.co/store_locator/fairview-pointe-claire-upper/', 'http://www.ccrepairz.com', 'http://www.woodiesautoservice.com', 'https://locations.jackinthebox.com/us/ca/concord/1710-monument-blvd', '1592269704', None, 'http://www.durbar.ca', None, 'http://www.9ontheplate.com', 'http://www.ntb.com/store/8495/huntersville-nc-28078-7148?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, None, None, 'http://www.vatocihairstudio.com/', None, 'https://caroun-restaurant.com', 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', None, 'http://www.timhortons.com/ca/en', None, None, None, None, None, 'http://www.beanandpearl.com', None, 'http://www.theeflowerzone.com', None, None, 'https://www.pubbricco.com', None, 'http://store-locator.barnesandnoble.com/store/2812', None, 'http://www.bk.com', 'https://www.haircutmensantanvillagegilbertaz.com', None, 'http://www.riopizza.co', 'http://www.consignonadime.com', None, None, None, None, None, 'http://thedippingwell.com/', 'http://www.eyesoncharlotte.com', None, 'http://www.lilliputtownecenter.com', None, None, None, 'http://kingswoodcreation.com', None, None, None, None, 'http://www.ashbridgesbayanimalhospital.ca/', '1592269785', 'http://www.estrellagolf.com/players-grill-patio.html', None, 'http://www.vantaggiohair.com', 'https://sacredhour.com', '1592269799', 'http://www.jackinthebox.com/', None, None, None, 'http://azhandwristspecialists.com/locations/phoenix-3rd-street', 'http://www.bootleggerssmokehouse.com', 'http://www.spicesmk.com', 'http://www.tangofoodtruck.com', 'http://www.tigermechanical.net', None, 'http://www.zanobia.ca/', 'https://www.udupicleveland.com', None, 'https://www.valuecityfurniture.com/store-locator/nc/charlotte/2320-sardis-road-north', 'http://www.stclair.org/about/find-a-location', 'http://www.yomamasgoodcookn.com', None, 'http://www.firstclassflowerscalgary.com', 'http://www.brownroaddental.com/', None, None, 'http://www.tbonesmarketplace.com', None, None, 'https://uniquebeautync.com', None, None, 'http://www.markhamgreen.com/', None, 'http://www.pizzaandgyroexpress.com/', 'http://www.ladiesgentlemen.com', 'http://www.arsenalciderhouse.com', None, None, None, 'http://www.cdwcharlotte.net/', 'http://www.phoenixmvhr.org', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://hornemazda.com', None, 'http://dragonchefchinese.com/home-page/', None, None, '1592269887', 'http://www.bankofamerica.com', 'http://www.skcigs.ca', 'http://www.eytcink.com', 'https://stores.advanceautoparts.com/nc/charlotte/2910-freedom-drive?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', 'http://www.rue21.com', None, None, None, None, 'http://thesman.com/las-palmas-phoenix-mesa/', 'http://revivemedspa.ca/', None, None, None, 'http://www.thepreserveapts.com/', 'http://www.pusateris.com/', 'http://www.healthsourcechiro.com', None, None, '1592269922', None, 'http://insanespeed.net', 'http://www.aimss.us', 'http://www.updatedautobody.com', None, 'http://www.poppyspizzatruck.com', None, 'https://locations.riteaid.com/locations/pa/imperial/103-west-allegheny-road.html', None, None, None, None, None, 'http://www.bestwaydryerventcleaning.com', None, '1592269945', None, 'http://www.chaudharylaw.com/', 'http://bulldogdetail.com', None, None, 'http://www.dayali.ca', None, None, None, None, None, 'http://www.vastraclothing.com', None, None, 'http://www.acexpertsaz.com', None, 'http://www.jungseed.com/JungGardenCenters.asp', 'http://www.charlottevegfest.com/', 'http://www.khloeshairstudio.com', 'http://www.macedoniaveterinaryclinic.com', 'http://www.homedepot.com/l/Mississauga-Heartland/ON/Mississauga/L5V-3E4/7132', 'http://www.theblackorchidaccessories.com/', None, None, 'http://jjlandapartments.com', None, None, 'http://nantha.com', 'https://www.springfreshcleaner.com', None, 'http://upmc.com/mercy', None, None, None, None, 'https://www.theyvc.com', 'https://www.mooregraphicsaz.com', None, 'http://www.beyondtransmissions.com/', None, None, 'http://www.markhampubliclibrary.ca/info/location_TC.asp', None, None, 'https://qmenu.us/#/yum-cha-las-vegas', 'http://miniso.ca', 'http://falbobrospizza.com', 'http://btlmassage.com', 'https://tours.asu.edu/tempe/packard-baseball-stadium', None, 'http://www.albertacourts.ab.ca/ProvincialCourt/tabid/70/Default.aspx', None, 'http://www.organiclifestyle.ca', 'http://www.wefrybread.com', 'http://www.theroyal.to/', 'http://www.merlenorman.com/', 'http://www.marketstreetkitchen.com', 'http://www.thewestsidebakery.com', None, None, 'http://aztecarestaurantcharlotte.com', None, None, 'http://www.icareoptometry.net', None, '1592270055', None, 'http://www.GarraSpas.com', 'http://www.goldinvegas.com', 'http://www.goodrebelvegan.com', 'http://www.artspacestudio.com', None, None, None, 'http://www.sallybeauty.com', 'http://www.celebritytanning.com', None, 'http://www.westfieldeyecenter.com', 'https://www.grooveryde.com', None, 'http://www.treasuresforyou.com', None, 'http://waterstreetdistrict.com', None, None, 'http://grizzlymassage.com', 'https://www.papajohns.com', 'http://www.emineomarketingsolutions.com', 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', None, 'http://www.lush.ca', 'http://www.lvccld.org', None, None, None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://sweetfrog.com/locations/store/sweet-frog-indian-trail-nc', 'http://www.doggiestylzlv.com', None, None, 'http://www.theducephx.com', None, None, None, None, '1592270133', 'https://www.goldencorral.com/locations/961/golden-corral-west-river-road-n', 'https://www.fkrestauranttoronto.com', 'http://usrlib.org', 'https://www.enterprise.ca/en/car-rental/locations/canada/qc/dollard-des-ormeaux-boulevard-des-sources-c701.html?mcid=iyp:8368400', 'http://www.ameliospizza.com', 'http://www.goldengreenhotel.com/', None, None, 'http://www.gloriaparkvillas.com', None, None, None, 'http://www.asccustomdetail.com/', None, 'http://www.btax.biz/', None, 'http://farahsalonspa.com', 'http://www.revolvecharlotte.com', 'http://www.zebreoptique.com', 'https://palazzohc.com', 'http://www.riparianinstitute.org/', 'http://www.mrwhitsettinc.com', None, None, None, 'https://www.nofrills.ca/store-locator/Emiliano+and+Ana%27s+nofrills+%28Dixon+Rd.%29/3480?storeId=3480', 'https://local.safeway.com/safeway/az/phoenix/810-e-glendale-ave.html', 'http://www.marriott.com/hotels/travel/yyzbm-courtyard-toronto-brampton/', None, None, None, None, 'http://www.tahitivillage.com/', 'http://www.officedepot.com', None, None, None, None, 'http://www.rawhide.com', None, 'http://www.peachwaveyogurt.com', 'https://www.methodspa.com', None, 'http://stgabrielmedical.ca', 'http://www.twobucks.us', 'http://www.acevending.net', None, 'http://leesatamember.com/locations/wphx/', 'http://www.browart23.com', 'http://www.foresthillphysiotherapy.ca', None, None, 'http://storelocator.staples.ca/stores/en_CA/ON/Etobicoke/11', 'https://biggtire.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.ljsilvers.com/', 'http://www.subway.ca', None, None, None, 'http://www.drgardocki.com', None, 'http://www.frankiesfamouspizza.com/', 'https://us.longchamp.com/store/longchamp-las-vegas', None, 'http://www.tanenvyspraytan.com', 'http://www.zales.com', 'http://www.wagoninn.net', 'https://www.hertz.com/rentacar/location/unitedstates/arizona/goodyear/PHXW33', None, 'http://www.hrcarpets.com', None, 'http://www.saladcreations.net', 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', None, 'http://www.pontevecchioristorante.com/', None, 'http://www.iautonc.com', 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', None, None, 'http://www.valleypain.org', 'http://tanlicioustanandlaserclinic.com', 'http://www.joeysnypizzas.com', None, None, None, 'http://www.knobhallwinerypgh.com', None, '1592270296', None, 'http://vegaspaintingcontractor.com', 'https://www.famousfootwear.com/?partnerid=YELP', '1592270305', 'http://www.oakvilletech.ca/', None, 'http://www.blissbridalboutique.ca', None, 'http://www.bk.com', 'https://www.escapology.com/en/las-vegas-nv/', None, 'http://www.windhorseairsoft.com', 'http://www.gatewayclipper.com', 'http://www.vegasnucca.com', 'http://www.picklesburgh.com/festival-schedule', 'http://beljanpsychologicalservices.com', 'http://jackspizzafc.com', None, None, None, None, 'http://www.theiconmadison.com', None, None, None, 'https://stores.savers.com/on/mississauga/savers-thrift-store-2027.html', None, 'http://www.stluciaapts.com/', None, None, 'http://www.europeandetail.com/', 'http://www.villasatstonecreek.com', 'http://superlube.com/ci/locations/details/509', 'http://www.dreamingsummitah.com', '1592270376', None, 'http://www.vegascrawl.com', None, None, 'http://www.telus.com', 'http://www.coldstonecreamery.com/stores/21109', 'https://www.hilton.com/en/hotels/cltblhx-hampton-charlotte-belmont-at-montcross/?SEO_id=YELP-HP-CLTBLHX', '1592270390', None, 'http://www.thevanityco.ca', 'https://blackdogcarwash.wordpress.com', None, None, None, None, 'http://www.lvaec.net', None, None, None, None, 'https://www.zippssportsgrills.com', 'http://www.pureliquidskinstudio.com/', 'http://www.montecellos.com/', None, 'https://diggersplumbing.com/mesa/', 'http://www.aroma.ca/', 'https://www.cvs.com/minuteclinic/clinic-locator/nv/lasvegas/10348.html', 'http://www.rwcphx.com/', 'http://www.abvi.com', None, 'http://www.sonnysbbq.com/', None, 'http://www.starrcleaningaz.com', 'http://razoremporium.com/', None, 'http://www.thesalondibella.com', None, None, None, None, None, None, 'http://www.regalauctions.com', 'http://www.rexsinnkeeper.com/', 'https://wojoteam.com', 'http://www.crabtree-evelyn.com/eng/stores/state/Nevada', 'http://www.aquienta.com', None, 'http://riopizza.restomenu.ca', 'http://www.goodlifefitness.com', None, None, None, None, 'http://www.anniethemaid.com', None, None, 'https://www.dundas427.com', None, None, 'http://www.biltmorehairrestoration.com', None, 'http://416wheelsandtires.com', None, 'http://www.tuxedorentalphoenix.com', None, None, 'http://www.brightwayinsurancecharlotte.com/', 'http://www.nevadachickencafe.com', None, 'http://www.wickedwaxinglv.com', 'https://stores.petco.com/pa/pittsburgh/pet-supplies-pittsburgh-pa-1812.html', 'http://blueheronmedina.com', None, None, None, 'https://corkale.com', 'http://www.tacobell.com', 'http://www.mpbconline.org', None, 'http://www.urbancookies.com', None, 'http://spatiniaz.com', None, 'http://www.salon77.ca', 'http://www.goldengatechinese.biz/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.flatsfixedbicycles.com/', None, None, None, None, None, None, '1592270545', 'http://www.marketon.com', None, None, None, None, 'http://www.cp911az.com', 'https://elrancho.igaarizona.com/contact-us/', 'http://phoblackbull.com', 'http://www.bedbathandbeyond.com', 'http://www.stopsmokinglv.com', 'http://www.wetnwildphoenix.com', None, None, None, 'http://www.theyogalounge.net/', 'https://www.americafirst.com/about/branches/branch-details.cfm?siteNo=104', None, '1592270573', 'http://www.BodyworksByJoel.com', None, 'http://www.andreascateringaz.com/', 'http://www.allhomesaz.com/', 'http://www.activegreenross.com', 'http://www.paradiselanes.ca/', 'http://www.teavana.com', 'http://www.azmeadco.com', None, 'http://levetto.com/', 'http://www.fanzorellis.ca', None, None, 'http://saharamississauga.ca/', 'http://www.azspaworld.com', 'http://www.pita2go.ca', 'http://retail.petro-canada.ca/default.aspx', 'http://www.poolbydesign.com', None, '1592270616', None, 'http://desertcarpetcleaner.com', 'http://chesterlandauto.com', None, 'http://www.gabinkorean.com', 'http://www.khanscope.com', 'https://www.electronicwizards.net', None, 'https://www.oneguardhomewarranty.com/contact/', None, 'http://justgrooming.com', None, 'http://www.barrospizza.com', None, 'http://tlex.ca', 'https://leosautocharlotte.com', 'https://www.statscharlotte.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.delsolapartments.com', None, None, 'http://www.gianteagle.com', None, 'http://www.littleluxuryspa.com', 'http://www.promptservicetoday.webs.com', 'http://windowtintingnorthphoenix.com/', None, None, 'https://www.walgreens.com/locator/walgreens-1725+northport+dr-madison-wi-53704/id=2967', None, 'http://www.strictlydiesel.com', None, 'http://lvsamuraibbq.mystrikingly.com', 'https://www.walmart.com/store/5186/gilbert-az/whats-new', 'http://www.caroldrake.com?cmpid=BZJC_BLM_0006', 'http://www.klfloraldesign.ca/?srccode=yelp_track', 'http://nuwu.vegas', None, None, None, 'http://www.kessleroptical.com', 'https://stores.mattressfirm.com/nv/northlasvegas/mattress-stores-north-las-vegas-nv-5322.html', 'http://www.trotzensports.com', None, '1592270695', None, None, 'http://www.myoreckstore.com', None, None, 'http://www.robwagnerautobody.com', 'http://www.firstclasslimos.net', 'http://www.2guyes.com/', 'http://www.kasamoto.ca', 'http://freshcouch.com', None, 'https://www.carolinashealthcare.org/locations/arboretum-pediatrics', None, 'http://www.skyviewdentistrycharlotte.com', None, 'http://quailhollowvet.com/', 'http://store.givenchy.com/107739-givenchy-las-vegas-wynn-women-men', None, None, 'http://www.buyandsellwiththisguyer.com', None, None, None, 'http://www.stonebrookdental.ca', None, 'http://philsny.com', 'http://agavepediatrics.com', None, None, 'http://www.talbots.com', None, None, None, 'http://kimchidelight.com', 'http://www.dunkindonuts.com', None, None, 'https://www.srpnet.com', 'http://www.thaishaninn.ca', 'http://www.chinastarbuffet1988.com', '1592270763', 'http://www.tommy.ca', 'http://www.boulevardvegas.com', 'http://www.streetsofnewyork.com', 'https://federicotirepainesville.com', 'http://www.millvalepa.com/businesses/millvale-diner', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.teamsmandych.ca', 'https://www.zeppes.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.03157.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03157', None, None, 'http://www.hairtipssalon.com', 'http://www.grinderspizzaloungemenu.com', 'https://stores.whitehouseblackmarket.com/en/yorkdale-shopping-centre', 'http://www.SladeGrove.com', 'http://magictouchcarwash.com/', None, None, 'https://www.phantomhookahlv.com', None, 'http://www.udderdelight.com/', None, None, None, None, 'http://www.earthworkslv.com', None, None, 'http://www.sugardonuts.com', None, 'http://www.clevelandymca.org/hillcrest-lyndhurst.html', 'https://www.extraholidays.com/las-vegas-nevada/worldmark-las-vegas-tropicana-avenue?lid=yelp&identifier=yelp&hotelid=77220&utm_medium=referral&utm_source=yelp-local&utm_campaign=yext&utm_content=wmlasvegas-tropicanaavenue', 'http://www.monaslounge.com/', 'http://www.geologicgallery.com/', None, None, 'http://www.competitionzero.com', None, None, 'http://thesuffolkpunch.com', None, 'http://www.kathleenrosehair.com', 'http://www.allcitytowing.com/', 'http://www.suncupcafe.net', None, 'http://www.brueggers.com', None, 'http://www.blockbuster.com', None, 'http://www.mybigfatgreekrestaurant.net', 'http://www.burgerking.ca', None, 'http://www.rashers.ca', None, None, None, 'http://www.swarovski.com/en-US/?utm_source=YELP&utm_medium=referral_managed&utm_campaign=YELP', None, None, None, 'http://www.kosama.com/tempe', 'https://www.bestjunkremovalnow.com', None, 'http://www.doggiecentral.ca/', 'http://l.macys.com/southpark-mall-in-charlotte-nc?cm_mmc=Yelp_Stores-_-Charlotte-_-n-_-787&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Charlotte_787&m_ac=yelp_stores&m_ag=n', 'http://www.purefacestudio.com', 'http://www.allwestfamilydentistry.com', 'http://whasn.com/main/doctors/38', None, None, None, 'http://www.nationalpawnshops.com/locations/charlotte-5418-south-boulevard', 'http://www.papamurphys.com', 'http://www.lilbrewhops.com', None, None, None, 'http://www.dangerousdansdiner.com', 'http://quickmuffler.com', 'https://iron-rooster.business.site', 'http://www.advancedspinenv.com', 'http://www.702-dentist.com', None, 'http://www.theinstantclassicslive.com', 'http://yummygarden.ca', None, 'http://www.piubella.ca', 'https://locations.aarons.com/us-az-mesa-4425-e-mckellips-rd-ste-109-store', 'http://www.perfectimageshairstudio.ca', 'http://www.evexiaspa.com', 'http://www.madisons.ca', 'http://www.yogurt-land.com/', 'https://www.usps.com/', 'http://www.mariospgh.com/eastside', 'http://www.bankofamerica.com', 'http://www.paulbunyansfirewood.com', None, None, None, 'http://www.livelovesummerlin.com', None, None, None, 'http://www.theedenbistro.com', None, 'http://www.eventessentials.com', None, None, 'http://www.bangkokthaimassagelasvegas.com', None, 'http://www.laocasionphoenix.com', None, 'https://www.bannerhealth.com/locations/glendale/banner-health-clinic-1', None, 'http://www.visionmobile.ca', 'http://www.midas.com/phoenix/store.aspx?shopnum=1395&dmanum=684001', None, 'http://www.leosicecream.com/', 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', None, 'http://www.dog-gone-beautiful.com', None, None, None, 'http://joyandvitalitycentre.ca', None, None, 'https://www.thesmithcenter.com/shows-tickets/cabaret-jazz/', None, None, None, None, None, 'http://www.mammaspizza.com', None, None, 'http://www.centurionrestaurant.com', 'https://satruck.org', 'http://www.nyandcompany.com', None, 'http://www.montanas.ca', 'http://www.natliving.ca', None, None, None, None, 'http://www.oldtownbuffetyu.com', 'http://www.tacobell.ca', None, None, None, 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', None, None, 'http://www.bluburger.com', None, None, '1592271048', None, 'http://www.antiquecitywarehouse.com', None, 'http://www.wokinexpress.ca/index.html', 'http://www.burlequeshowlv.com', None, None, None, None, 'http://www.virginiashouse.com', None, None, 'https://www.danielsjewelers.com/Online_Application_Starts.cfm', 'http://www.liveataltagrove.com', 'http://www.mekongriver.ca/', None, None, 'http://www.vegasxtremepaintball.com/', 'http://www.corefitnessaz.com', 'https://www.westerndental.com/en-us/find-a-location/arizona/peoria/8392-w-thunderbird-rd', 'http://www.greatclips.com', None, None, 'http://spanishpalmslv.com/features/', 'http://onyxbarbers.com', 'http://www.octopusgardenyoga.com/', 'http://www.sallybeauty.com', None, 'http://local.firestonecompleteautocare.com/arizona/queen-creek/18467-e-queen-creek-rd/?lw_cmp=IYP_YPC_MLP_784293', None, None, 'http://www.jiffylube.com', 'http://www.gooddogfoodcompany.com', None, 'https://www.smartstyle.com/en-us/locations/nv/las-vegas/located-inside-walmart-3473-haircuts-3334.html', None, None, None, None, 'https://www.cellairis.com/store-locator', None, None, None, None, None, 'http://www.fantasycarrentals.com', None, 'https://www.ilovekickboxing.com/studio/index.php?id=674', 'https://www.kingsautoglasslasvegas.com', None, None, 'http://www.vincentsgreentree.com', None, None, None, 'https://locations.vitaminshoppe.com/az/avondale/vitamins-supplements-avondale-az-229.html', None, None, 'http://www.makohair.com', None, 'http://www.famechurchlasvegas.com/', None, 'https://www.nhospt.com/contact', None, 'http://www.salsaritas.com', 'http://www.villageicecream.com', 'http://pizzafusion.com/henderson/', 'http://www.villaserenahenderson.com', 'http://www.importsbyday.com', None, None, None, None, None, None, 'http://www.bakersolarandelectric.com', '1592271176', None, 'http://www.trca.on.ca/enjoy/locations/bruces-mill-conservation-area.dot#sthash.F8hQCB9Q.dpbs', 'http://saddleupsaloon.org/saddleupsaloon/page.html', 'http://www.contisshoerepair.com', 'http://www.toryburch.com', None, None, None, 'http://www.justforyouintempe.com', None, None, None, 'https://agents.farmers.com/az/mesa/frank-margiotta?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', '1592271197', 'http://www.backtoyoung.com/', 'https://www.familydollar.com/locations/pa/pleasant-hills/25224/', None, None, None, 'https://www.chilis.com', 'http://www.bowl300az.com', None, '1592271209', None, None, None, None, 'http://www.jacquelinescafe.com', None, 'http://www.animalzen.net', None, 'http://spaghettiandco.net', 'http://discoveryharbor.net/', 'http://www.loud-pedal.com', 'https://jcncourier.com', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', 'https://www.tobaccoleafvegas.com', None, '1592271237', 'https://www.chapters.indigo.ca/fr-ca/accueil/localisateurdemagasins/detailsdumagasin/794/?link-usage=Header:+Fran%C3%A7ais', 'http://habanerosmg.com/habaneros/home.html', None, None, 'http://www.ahwatukeeoralsurgery.com', 'https://www.sunsetgrill.ca', None, None, 'http://www.barefootarchery.com', 'http://www.oakwoodfamilydentalcare.com', 'http://www.clevelandyoga.com', 'http://www.popdeluxe.net', None, None, None, 'http://www.charlottepediatricclinic.org', 'http://www.redrockcanyonlv.org/hikes-trails/lost-creek-childrens-discovery', None, 'http://www.pizzeriadeisassi.ca', 'http://www.mrplumbingaz.com', None, 'https://salsaritas.com/page/locations/nc/denver/112-highway-16-s/?vendorCampaignCode=google-177', None, 'http://www.cornerstoneflooringaz.com', 'http://www.clevelandcitydance.com', None, None, None, None, 'https://www.scottrepman.com', None, None, None, None, None, None, 'http://www.rolledicecream.com', 'http://perfectionpaintingpros.com', None, 'http://countrybarphoenix.com/', None, None, 'http://www.hairbossextensions.com', None, None, None, 'https://ezshreddingsolutions.com', None, None, 'https://pitapit.ca/location/#/en/oakville-maple-grove', 'http://magnoliahouseflorist.com', 'http://www.vueparkwest.com/', 'http://bongbella.com/', None, 'https://www.orangetheory.com/en-us/locations/ohio/strongsville/18105-southpark-center/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.chagrincakes.com', 'http://www.petestransmissionaz.com', 'http://www.bebe.com', 'http://www.officemax.com', None, None, '1592271321', None, 'http://YaBikes.ca', None, 'http://www.yourfascinations.com', None, 'http://www.dollartree.com', None, None, None, 'http://waterdamagevegas.com', 'http://www.nicenails.ca', None, 'http://www.the-grove.com/', 'https://battleaxedesigns.com', None, 'http://www.blindstogo.com/en/stores/davenport?ua=Toronto%2C+ON+M5R+1J9%2C+Canada&rds=25', None, None, None, 'https://www.asu.edu/', 'http://www.generalsolaraz.com', 'http://www.rincon-peruano.com', None, 'http://www.gibsonscleaners.com/', 'http://turkishkebabhouse.net', 'http://www.anjolique-bridal.com', 'http://www.themartin.com', None, 'http://www.sewsassyquiltshop.com', 'http://www.cobblestoneaptsphoenix.com', 'http://salsaritas.com', None, 'http://www.bluivorybridal.com/', 'https://ytr.com/solon/', None, None, None, None, None, None, 'https://www.kungfutea.com', 'http://www.pinktheboutique.com/', 'https://www.rosedalecomputers.com', None, 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://missiontreatment.com/locations/nevada/las-vegas', 'https://www.chixeggshop.com', 'https://www.supercuts.com/locations/sc/tega-cay/stockbridge-commons-haircuts-81186.html', None, None, 'http://www.greatclips.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.seespotonline.com', 'http://pizzeriaprontolv.com', None, None, 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://www.onceuponachildrichmondhill.com', 'http://cocoespressobar.com', None, 'http://windowtinthenderson.com', None, '1592271432', 'http://www.romeospizza.com', 'http://yourbeautyperfected.com', 'http://www.islandstorageaz.com', 'http://www.thehotb.com/', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.lifetimeautomotiveaz.com', '1592271450', None, None, 'http://www.meders.com/default.html', 'http://summerbirdboutique.com', 'http://www.towerautosales.com/', 'http://www.hairbyjoshuapaul.com', 'https://megafurnitureusa.com', 'http://www.zoesstore.com', None, 'https://www.orangetheory.com/en-us/locations/ohio/n-olmsted/26092-brookpark-rd/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.stussy.com', None, 'http://www.babur.ca/', None, None, 'http://www.sherwin-williams.com/store-locator/paint-store/Las%20Vegas/NV/8114', 'https://www.kelseys.ca/location_region.php?province=on&s=1&city_drop=Aurora', 'http://jumpSkypark.com', None, None, None, 'http://fibetv.bell.ca/en/features/introduction/', 'http://www.purrfurredpets.net', None, '1592271490', None, None, 'http://www.houseofshoesonline.com/', 'http://www.closetsconsignments.com/Closets/Welcome_To_Closets.html', None, None, None, None, 'https://mr-alkaline-water.business.site', 'http://recreatespainc.com', None, 'http://www.yappyhourbakery.com', 'http://www.royalhotelvegas.com', None, 'https://www.rosatispizza.com/location/tempe-az/', 'https://www.aliantegaming.com/dine/fine-dining/mrkt', '1592271522', None, None, 'http://www.oasismedicalclinic.ca', 'https://www.jusubar.com', None, None, None, None, None, None, None, None, None, None, 'http://www.nedskrazysub.com', None, 'http://ubburger.com', 'https://www.aqua-tots.com/ballantyne', 'http://www.arbys.com', None, None, None, 'http://www.1800flowersphoenix.com', 'http://www.americastacoshop.com/stores/14009', 'http://www.groundround.com', None, 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=101357', None, None, None, None, None, None, None, None, 'https://www.fasturtle.com/contact/phoenix/', 'http://www.carolinafamilydentistry.com', 'http://www.nalamedspas.com', 'http://www.erinmills.ca', '1592271590', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.arvocoffee.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.vineexpressions.com', None, '1592271605', 'http://aaaa-az.org', 'http://allprocarpetandtilecleaning.com', 'https://www.aldosrestaurant.com', 'http://www.bishopspizza.com', 'http://www.pitanutso.com', 'http://www.avalonmeatcandy.com', None, None, 'http://www.gnc.com', 'http://www.harveys.ca', None, '1592271626', None, 'http://www.thehearthandpatio.com', 'http://www.suntrust.com', 'http://www.cookout.com', None, None, None, 'http://www.raptorplumbing.com', 'http://www.pumpkinpecan.com', None, 'https://www.markscafeaz.com', 'http://www.oldnavy.com', 'http://www.phoenixtowingservice.com', None, None, None, 'http://scottsdale.schoolofrock.com/?labelSource=Yelp&utm_campaign=yelp&utm_source=yelp&utm_medium=yelp&utm_content=yelp', 'http://www.FourSeasonsMotorCompany.com', None, None, 'http://www.dibellas.com/club-bread?source=yelp', None, 'http://hudecdental.com/office-locations/broadview-heights-oh', 'http://www.dinopalmierisalon.com', 'http://www.petitethuet.com/', 'http://www.barbotanico.com', None, 'http://pca.pittsburgharts.org/', 'http://www.avictoryhotels.com', None, None, '1592271685', None, None, None, 'http://3mincarwash.com', None, None, None, 'http://www.zephyrcleanair.com/', 'http://ci.champaign.il.us', None, 'http://www.fatjacksbbq.biz', None, 'http://www.bestmatt.com/', None, 'http://www.patcatans.com/craft-store-locations/cuyahoga-falls-oh', None, 'http://neteffectcafe.com', 'http://www.aaa.com', 'http://www.charlotterestaurantweek.com', 'http://www.exilecreative.com/', None, 'http://kol3restaurant.com/', None, None, 'http://www.jamaicahouserestaurant.ca/en/', None, None, None, 'https://www.wingzone.com/charlotte/', 'https://www.exaltarestaurant.com', 'http://clicks.dbm-media.com/Yelp_mobile', 'http://www.westwinddriveins.com/westwind/index.php?r=drivein/location&idtheater=614', 'http://www.everydaycoffee.com', 'http://www.allamericandave.com', 'http://www.champssports.com', 'https://www.chick-fil-a.com/scottsdale101', None, 'http://www.ruelo.com/', None, None, 'https://www.mountainshadows.com/dining/hearth', None, None, 'http://www.gohongkongrestaurant.com', None, '1592271766', 'http://www.messingermortuary.com', 'http://nicolejamessalonandspa.com', None, None, None, 'http://www.cactusranchmadison.com', None, None, 'https://lvnicsbs.com/physicians/jason-e-garber-md-facs/', None, 'http://www.CestLaVieLounge.com', 'http://tailormadetattoo.com/', None, 'http://www.andrewsosborne.org', None, None, None, None, None, 'http://www.atlasorientalrugs.net', None, 'http://www.paprikahouse.ca', None, 'http://www.empiricalsound.com', 'http://www.phandds.com/', 'http://www.totspotpreschool.com/', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', 'http://santecares.com/locations/sante-of-surprise/', None, None, 'http://www.speakeasy21.com/', 'https://Parklawn.orangetheoryfitness.com?utm_campaign=yelp&utm_term=072017&utm_medium=print&utm_source=redirect&utm_content=yelp_print', None, None, None, None, None, 'https://www.aritzia.com/en/store-locator?q=+L4J+4P8&view=results', 'https://www.homedepot.com/l/Chardon/OH/Chardon/44024/8981?cm_mmc=seo-yelp&', None, 'http://binalipizzamenu.com/', 'http://www.silverminesubs.com/', None, 'https://www.choicehotels.com/north-carolina/huntersville/quality-inn-hotels/nc407/rates', 'http://www.btacollision.com/', 'http://www.renspets.com', 'http://www.ipolished.com', None, None, 'https://avintivmedia.com', 'https://www.lumberliquidators.com/ll/stores/az/chandler/2460-e-germann-road?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1222', 'http://www.sunridgebadminton.com', 'http://www.absolutelyinc.com/', '1592271872', 'http://www.airrepairnc.com', None, None, 'http://www.zelenskytherapy.com', None, 'https://www.choicehotels.com/nevada/henderson/comfort-inn-hotels/nv070/rates', None, None, None, 'http://www.vegasdiscountnutrition.net', 'http://www.earthbloorwest.com/', 'http://jcfamilydentalaz.com', '1592271894', None, 'http://www.steampluscarpetandfloors.com', 'http://fourbarrelhollys.ca', 'http://www.pizzaandpastavilla.com', 'http://doc.nv.gov/Facilities/CGTH_Facility/', 'https://www.steaksandhoagies.com', 'http://www.chevron.com/', None, 'http://www.valleyradiologists.com', 'http://abundantair.vegas', None, '1592271922', 'http://www.cocosbakery.com/', 'http://www.associatetax.com', 'https://www.idealimage.com/medspa-locations/arizona/phoenix-area/scottsdale', 'http://www.familypaw.com', None, 'http://scottsdalepsychic.com', None, 'https://locations.wendys.com/canada/on/pickering/742-kingston-road', None, None, None, 'https://www.circlek.com/store-locator/us/gilbert/888-s-higley-rd/2703373', None, None, None, '1592271958', None, '1592271961', 'http://www.fiftyonewings.com/', 'http://www.maxmuscle.com', 'http://www.bathandbodyworks.com', None, None, None, 'http://www.stingerssportsbar.com', 'http://www.bistrostsauveur.com', 'https://www.myfitfoods.com/', None, 'https://www.heatherdowns-apts.com', None, None, None, 'http://www.thedi.ca/', 'http://www.wimpysdiner.net', None, 'http://www.toronto.ca/parks/prd/facilities/complex/640/index.htm', 'http://beapaintmonkey.com', 'https://www.carstar.ca/en/locations/on/toronto-etobicoke/carstar-etobicoke-north-16215/', None, None, 'https://www.themovingguyaz.com', 'https://cashtime.com/loan-center-details/3241-e.-mcdowell-rd.-phoenix-az-85008', 'http://www.affordablepowdercoat.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, 'http://www.donpablos.com/', 'http://www.hotdealsauto.com', None, 'http://lishnailsalon.com/', 'http://www.honeysalt.com', 'http://www.pritchetteyecare.com', None, 'https://www.kindercare.com/our-centers/las-vegas/nv/000290?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=000290', 'http://www.simplymaidz4less.com', None, None, None, 'http://lakepleasantdentistry.com', 'http://www.apnapunjabcalgary.com/apnapunjabsweets/index.html', 'https://becklemusicstudio.com', None, None, 'http://thesonschildren.com', None, 'http://www.redwingshoe.com', None, None, 'https://www.karatekrav.com', None, 'http://ashleebowerdmd.com', None, 'http://www.ParisInScottsdale.com', None, 'http://www.mccoyspubonline.com', 'https://www.target.com/sl/mesa-west/1429', 'http://www.brinksinc.com', 'http://www.lyonsptlv.com', 'http://www.sequoiameadows.com', 'http://www.krudar.com/krudarkensingtoncontact', None, 'http://clevelandbanya.com/', 'http://www.alleghenysmokeworks.com', 'http://www.lookingglassadventures.com/', None, None, None, None, None, None, None, '1592272146', 'http://garrisonlawfirm.com/', 'http://www.sallybeauty.com', None, 'https://locations.massageenvy.com/arizona/chandler/4985-s-alma-school-rd.html', 'http://elitetowingandtransportservices.com', None, 'http://www.quiktrip.com', None, None, 'http://haikuthai.com/', 'http://www.gnc.com', None, None, 'http://www.foxsportsgrill.com/scottsdale', 'http://nlmwholeliving.com', 'http://www.winebarkensington.com', None, None, None, None, None, None, None, None, None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280218612&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.inspireglass.com', 'http://www.southwestlendingcloset.org', 'http://www.zuch-perio.com', 'http://www.7-eleven.com/?yelp=29384', 'http://www.bootcamplasvegas.com', 'http://www.scottsdalemedcenter.com', 'http://piazzatalarico.com', 'http://www.bookcity.ca', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', '1592272238', '1592272242', None, None, None, 'https://www.moneytreeinc.com/branch/north-nellis', 'http://goodearthcoffeehouse.com', None, 'http://www.waxcenter.com/pa-bethel-park?utm_source=yelp&utm_medium=cpc&utm_campaign=7GSquxGDRpjNblgYqIbrng', None, None, 'http://boostmobile.com', 'https://www.sephora.com/happening/stores/toronto-eaton-centre', None, None, 'https://haircutmenrockyriveroh.com', None, 'http://www.questdiagnostics.com', None, None, None, '1592272288', None, 'http://tacos-calafia.business.site', None, None, None, None, 'http://www.jensenselitedetail.com', None, None, None, 'https://www.thetrustedplumber.com', None, 'http://www.jacob.ca/', '1592272314', 'http://www.azfunparty.com/', 'http://www.dsw.com', None, 'https://www.thclegalgroup.com', 'http://www.charbar7.com', None, 'http://www.filibertos.com', None, 'http://www.smilesbydrhadley.com/', 'https://des.az.gov', 'http://www.yilo.com', 'https://www.amayarestaurant.com/locations/', 'http://www.colonial-wine.com', None, None, None, None, None, None, None, None, 'http://www.lagabiere.com', 'http://www.corerevclt.com', None, None, None, None, None, None, None, None, None, 'http://www.brassvixens.com', 'http://www.cityofhenderson.com/municipal-court/about', None, None, 'https://cannolicastle.us', None, 'http://www.alasvegasmedicalgroup.com', None, None, 'http://www.pho-huong-que.com', None, None, 'http://www.sizzloz.com', 'https://ablelockkey.com', 'https://www.aztecspringsisyourhome.com/aztec-springs-apartments-mesa-az', None, None, 'http://www.tantramadison.com', None, 'http://www.quickycarwash.com', 'http://www.ahillnotary.com', 'http://www.duncanshobby.com/index.html', None, None, None, None, 'http://ironquilltattoo.com', None, None, None, 'https://www.firehousesubs.com/locations/wi/oakbridge', 'https://pitapit.ca/location/#/en/ajax', 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', 'https://nevadaeyephysicians.com', None, None, 'http://www.bombchellestudio.com', 'https://www.rentanapt.com/apartments/az/chandler/sky-at-chandler-airpark/', 'http://www.gigisconsignmentboutique.com', None, 'http://www.acerentacar.com/landing/Canada/Dorval/Montr%C3%A9al%E2%80%93Trudeau-Intl-Airport.aspx', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.jennattar.com?cmpid=nyuj_blm_0006', 'http://www.ediblearrangements.com', None, 'http://www.ashleighphairstudio.com', None, None, 'http://aladdinmarket.ml', None, 'http://www.sullysboxinggym.com', 'http://www.tenthousandvillages.com', None, None, None, 'http://binkleysrestaurant.com', 'http://www.lakeerielimo.com', 'http://www.noodleandriceaz.com/', None, None, None, 'http://www.2550university.com', None, None, None, None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, None, 'https://freedompizzadeli.com', 'https://locations.jackinthebox.com/us/az/mesa/525-n-stapley-dr', None, 'http://www.weirdrealms.com', None, 'http://www.labelleparadisespa.com', 'http://www.twirlchandler.com/', None, 'http://www.lashedbynathalie.com', None, None, None, 'http://www.societycleveland.com', 'http://www.metrobarandkitchen.com/', 'http://www.nofrills.ca', 'http://dine.to/sites/labrasserie/', None, None, None, 'https://clean-mart.com', None, None, 'http://www.carolinaliceremoval.com/', None, None, 'http://www.niemeyerimports.com', 'https://www.vinoveritascellarscle.com', '1592272577', None, None, None, None, 'http://www.urodoc.net', None, None, 'http://www.timhortons.com', None, None, None, 'https://flowersbydonka.com', 'https://www.northcapresidential.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, None, 'http://www.tuscanytheatre.com/', 'http://www.sticksandshakes.com', None, 'http://luckydragonlv.com/320-2', 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'http://drfeatherstone.com', 'http://thebeautyconcept.ca', 'http://www.eternalsalon.com', None, 'https://www.kfc.ca//store/415-mount-pleasant-rd-toronto', 'http://www.leyvastowing.com', None, 'http://www.comptonsautomotive.com/', 'http://www.mypolishnails.com/', None, None, 'https://emsworth-inn.business.site', 'https://www.supercuts.com/locations/pa/pittsburgh/shadyside-plaza-s-highland-haircuts-8953.html', None, None, None, None, None, 'http://www.mammaspizza.com', 'http://www.wirelesstoyz.com', 'http://jonesgordon.org', None, 'https://www.mountaindentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'https://www.starbucks.com/store-locator/store/1022799', 'http://fukudapgh.com', 'http://www.AmericanTurfCo.com', 'http://www.thefishshoplv.com/', None, 'http://www.shoppersdrugmart.ca', None, None, None, 'http://www.7-eleven.com/?yelp=29641', None, 'http://www.thedrakehotel.ca/dining', None, 'http://www.ourfamilyeyecare.com', 'http://www.starbucks.com/store/15154/', 'http://www.ericreussmd.com', 'http://www.porsche-design.com', None, 'https://www.sheetz.com', 'http://www.cafefresh.com', None, None, 'http://www.fitness5gym.com', None, None, 'http://www.cornerstonefurniture.ca/', None, 'https://www.superlmarket.com', None, 'http://www.atozpain.com', None, 'http://www.mailingmore-craig.com', 'http://www.ratcliffeonthegreen.com', None, None, None, None, 'http://www.mptempe.com', 'http://www.starbucks.com/store/11135/', None, None, 'http://www.passioncellars.com', 'http://www.craftycrabrestaurant.com', 'http://www.terravisioncare.ca', None, 'https://www.massageplusbodywork.com', 'http://www.waxcenter.com/nv-las-vegas-lake-mead?utm_source=yelp&utm_medium=cpc&utm_campaign=uF-iSKRLBDZFeXNzA4xnEw', 'http://primepizzeria.net/', 'http://afterthebirth.biz', None, '1592272745', None, 'http://www.humblepieusa.com/', 'http://www.kimschooltaekwondo.com/', 'http://tlmobilecarwash.wixsite.com/wash', 'http://www.JimmyJohns.com', None, None, 'https://www.workuity.com', 'http://www.pemreg.com', None, None, None, None, 'https://stores.advanceautoparts.com/nc/charlotte/2910-freedom-drive?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', 'https://andersondentalaz.com', 'http://www.maryshiatsu.com', 'https://www.edwardhotel.ca', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', None, 'http://www.g-orthostudio.com', 'http://www.jnsfinaltouch.com', None, None, None, 'http://www.rykenchiropractic.com', 'https://agioristorante.wordpress.com/', None, 'https://thompsonlandscapingaz.com', None, None, None, None, None, 'http://goldenspoontakeout.com', 'http://www.krispykreme.com', None, 'http://www.dominos.com', 'http://www.starbucks.com', None, None, 'http://www.jackfrostdonutsusa.com', None, None, 'http://www.catawbaanimal.com', 'http://losfavs.com', None, None, 'http://Www.steeltowneinn.com', 'http://foodienorth.com', 'http://www.traditionalfishandchips.ca/', 'http://www.wagnerdentist.com', 'http://www.famousfootwear.com/?partnerid=YELP', None, None, 'http://www.birdseyeimaging.com/', None, None, 'http://www.jysk.ca/', None, None, 'http://www.owlfamily.ca', 'http://www.summitcoffee.com/outpost', 'http://www.goodlifefitness.com', None, 'http://www.nipashauto.com', 'http://www.brokerypropmgmt.com', None, None, None, None, 'https://www.indiegogo.com/projects/ogden-s-north-street-diner#/', 'http://coredental.ca', 'https://federicosmexicanfood.com', 'http://www.carcone.com', 'http://www.kamanawana.com', None, 'http://www.topnotchbarbeque.com/', None, None, 'http://www.miracle-ear.com', None, None, None, None, None, 'http://www.valero.com', None, 'https://www.tacobell.ca/fr/store/1595-cote-vertu-st-laurent', 'http://www.themadisonblind.com', 'http://www.nipponautoworks.com', None, 'https://www.signaturestyle.com/locations/il/champaign/cost-cutters-town-center-haircuts-62173.html', None, 'https://www.plazahotelcasino.com/real-results-gym/', None, 'http://www.thairoom.ca/', 'http://ae-herps-and-exotics.business.site', None, None, None, None, None, 'http://www.accreditedinspections.com', None, None, None, 'http://www.manchesterautoandtire.com/', 'http://www.autobathouse.com/category/9006/auto-bathouse-car-wash-in-plum-pa.htm', None, None, 'http://www.k-9kingdom.com', None, None, 'https://www.1800gotjunk.com/ca_en/locations/junk-removal-toronto?utm_campaign=yelp&utm_medium=ubl&utm_source=toronto', 'https://www.eyedoctorchandler.com', None, 'http://www.cleaningdoctorservices.com', None, None, None, 'http://www.udvegas.com', 'http://www.moneyexchangeworld.com/', None, None, 'http://www.smallcakescupcakery.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'https://www.littlehardware.com', 'http://urbanarttattoo.com/about/locations/ua3', 'http://l.macys.com/southpark-mall-in-charlotte-nc?cm_mmc=Yelp_Stores-_-Charlotte-_-n-_-787&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Charlotte_787&m_ac=yelp_stores&m_ag=n', None, None, 'https://madura-dine-in.business.site', 'http://www.antiqueroofingtile.com/', None, None, None, 'http://rochellessalon.com/', 'http://www.non-stopentertainment.com', None, None, 'https://www.signaturestyle.com/locations/on/aurora/first-choice-haircutters-51440.html', 'http://storelocator.staples.ca/stores/en_CA/ON/Brampton/217', 'http://www.ampm.com', None, 'https://www.americasbest.com/store-list/champaign-il-61822/', None, 'http://matthewsata.com/', None, 'http://azautotops.com', 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'http://locations.einsteinbros.com/az/scottsdale/6501-e-greenway-pkwy-bldg-5.html?utm_source=storelocator', 'http://www.filibertos.com', 'http://www.elitepawspa.com', None, None, None, None, 'http://www.sweeterytoronto.com', 'http://theupsstore.ca/29', None, 'http://www.leslievillecheese.com', 'http://www.goodlifefitness.com/locations/ontario/northyork/don-millseglinton?source=yelp-websitelink-northyorkdon-gl', None, 'https://www.carquest.com/stores/nv/las-vegas/14974', None, None, 'http://www.blackangus.com', 'https://www.guns2ammomesa.com', None, 'http://handsonhealing.amtamembers.com/', None, None, 'https://www.eddiev.com/', None, 'https://www.aztecshuttersphoenix.com', 'http://www.eyemasters.com/', 'https://www.signaturestyle.com/locations/wi/monona/cost-cutters-pier-37-haircuts-16030.html', None, None, 'http://www.paperandhome.com', None, 'http://ambiantdance.com/', None, 'http://www.saluf.com/', 'https://www.footankleaz.com', 'http://www.roerlaw.com', 'https://www.csn.edu/locations/summerlin-center', None, None, None, None, 'http://simplypurrfectgrooming.wordpress.com', None, 'http://www.dogpeopledogdaycare.com', 'http://whasn.com/main/doctors/27/24', 'http://amberbrewery.com/?page_id=121', None, None, None, None, None, 'http://www.azflowerbar.com', 'http://www.deltaco.com', None, 'http://eastcoastcustard.com', None, 'http://www.mymacchiatos.com/', 'http://www.thornhilltints.com/', 'http://www.pinevillehomes.com/', 'https://www.stviateurbagel.com', None, 'http://www.speedy-air.com', 'http://www.dunkindonuts.com', None, None, 'https://www.phoenix.gov/parks/golf/phoenix-golf-courses/palo-verde', 'http://www.ultimate-outdoors.net', 'http://www.coffeerushcafe.com', 'http://www.thepriory.com', None, None, 'http://www.azbestwindows.com', None, 'http://www.thecozyhomemadison.com', None, 'http://www.cariboucoffee.com/', None, None, 'http://www.aquasafeswim.com/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Yelp-Ads', 'http://sophieskitchen.ca', None, 'http://accentglassinc.com', 'http://locations.michaels.com/nc/charlotte/5032/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', None, 'http://rewardstravelchina.com', 'http://www.mississaugachinesecentre.com', 'https://www.lithuanianhouse.ca/bar-lokys', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', None, 'https://statovernight.com', '1592273141', None, 'http://www.quiktrip.com', None, None, 'http://www.menchies.com/', None, 'http://worldofbeer.com/Locations/Lakewood', 'https://locations.dignityhealth.org/weight-loss-surgery-center-at-st-rose-dominican-henderson-nv-henderson-nv', 'http://www.handandstone.com/spa/store/Beachwood', None, 'http://www.thecowfish.com', 'http://www.lucirestaurant.com/', None, 'http://www.ihg.com/holidayinn/hotels/us/en/madison/msntc/hoteldetail/dining', 'http://www.skincarebyklara.com', None, None, 'http://millennium605.com', 'http://www.markhamphysiotherapist.ca', 'http://www.flyfar.ca/', None, None, 'http://www.broadmoornails.com', 'http://www.neohioeye.com', 'http://www.baskinrobbins.com', 'http://castillolawphoenix.com', None, 'http://www.sammyspastrami.com', 'https://www.chick-fil-a.com/rivergate', 'http://mtbmovingcompany.webs.com', 'http://azbugcontrol.com/', 'https://locations.theupsstore.com/ca/concord/1647-willow-pass-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://www.soaknailshop.com', None, None, None, 'http://www.cnautodetailing.com', None, None, None, None, 'http://www.silverliningestatesalesnv.com', None, None, 'http://www.whittonplumbing.com', 'http://www.limitedbrands.com', None, 'https://1313crossfit.wixsite.com/crossfit1313', 'http://www.desertshieldglass.com', 'http://www.vegaspooltablemovers.com', 'http://www.fiammaristorante.ca', 'http://www.themusikbox.net', 'http://harpervalleyptair.com', 'http://www.valley.md', 'http://www.totaltanaz.com', 'http://www.salonyounique.com', 'http://www.sidneydairybarn.com', None, 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://phxbike.com/', None, 'http://tattooingu.com', None, 'https://www.bobevans.com/our-restaurants/locations/2005?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', None, 'http://bbbfashionaz.com', None, 'http://www.starbucks.com/store/15154/', '1592273275', None, None, None, None, None, 'http://www.markhamgolfdome.com/', None, None, '1592273288', None, 'http://www.coldstonecreamery.com/stores/23576', 'http://firesidepublichouse.com', None, 'http://racacafeandbar.com', None, None, 'http://www.estatehouseaz.com', 'http://www.therapeuticsole.com/', 'http://www.mississaugaitalfest.com', 'http://www.dynamicautoglassaz.com', None, None, None, None, 'http://www.wagnersofwestlake.com', None, None, '1592273319', 'http://www.costco.ca/warehouselocatordetailsview?langId=-24&storeId=10302&catalogId=11201&warehousenumber=1076&beginaddress=calgary&numofwarehousestoreturn=null&location=calgary&callingpage=warehouselocatorview', None, None, None, 'http://www.affordabletowncarservice.com', 'https://parsonsvillas.com', 'http://www.kitchenandcouch.com', 'http://joeysurban.ca/menus.php', 'http://clickserve.dartsearch.net/link/click?lid=43700006435127850&ds_s_kwgid=58700000444950640&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.troyshoppejewellers.com', None, 'http://www.tacodelmar.com/', 'http://www.hairbyjingles.com', 'http://www.balloonslasvegas.com/', 'http://www.gallomiller.com', 'http://jonasrestaurant.com', 'http://swampt.net', 'http://gridbikes.com', None, None, None, None, None, 'https://ad.doubleclick.net/ddm/clk/458940992;262997184;h', None, 'http://www.dollartree.com', None, None, 'http://www.fix24wellnessstudio.com/', None, 'http://www.kernlawoffices.com', None, 'http://www.closetothebone.ca/', None, 'http://www.rescuemyspeech.com', None, None, '1592273391', None, None, 'http://www.2birdsshuttleanddetail.com', None, None, None, 'http://www.bellsmartialarts.ca', 'http://boutiquebar.ca/', 'http://sagegardencatering.com', 'http://www.edmarshalljewelers.com', 'http://centercare.net/', 'http://www.theneonrun.com', None, 'http://www.bing.com/movies/search?q=Harkins%20SanTan%20Village%2016%20&FORM=DTPSHA', 'http://www.robertjpriceddspc.com/', 'http://www.marsfood.ca', 'http://showmars.com/locations/south-park', None, 'http://www.elpolloloco.com', None, 'http://www.honefitness.com/', None, 'http://www.nandk.ca', None, None, None, None, '1592273441', 'https://www.dillards.com/stores/great-lakes-mentor-ohio/0362', None, None, None, 'https://sunsetstation.sclv.com/Dining/Cabo.aspx', None, 'http://www.nuagefitnesscenter.com/', 'http://www.pebblestonecoatings.com', None, None, 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1231', None, None, None, 'http://lilynailsalon.net', None, 'http://www.desertrat.com', None, 'http://osptempe.com/', 'http://www.westsidemarket.org/vendor.aspx?id=136', 'http://www.phoenicianhealth.com', 'http://www.yogurtology.com', '1592273486', None, 'http://www.lvcpas.com', 'https://greatroomescape.com/cleveland/?utm_source=yelp&utm_medium=websiteclick', None, None, None, 'http://www.stewart.com/commercial/las-vegas', 'http://www.penzeysspices.com', 'http://www.krispykreme.com/', 'http://www.mimiscafe.com', None, 'http://tegacaysc.org/facilities/facility/details/Windjammer-Park-1', None, None, 'http://www.siliburgers.com', None, None, 'http://www.stupidburger.ca', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://lampertsmarket.com', None, 'http://paintballparadyes.com/', 'https://www.agelessmenshealth.com/locations/las-vegas-summerlin-testosterone-replacement-clinic/', None, 'http://www.springvalleyautosales.net', None, 'http://rasovara.ca', None, None, 'http://www.earlbaleswalkin.com', 'http://www.onetwosnack.com', 'https://order.papamurphys.com/menu/papa-murphys-greenway', None, None, None, None, None, 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/calgary-3315-32nd-avenue-ne.aspx?storeid=12&code=pc', 'http://www.marshallscanada.ca/', None, 'http://www.changjiangmounthoreb.com', None, 'http://waverlydentalgroup.com', None, 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.mybugguardian.com/', 'http://www.donsitts.com', None, None, 'http://www.planetorganic.ca', None, None, None, None, None, None, 'http://www.thestonesurgeon.com', 'http://www.valleypaincenters.com', None, None, None, 'http://www.bk.com', None, None, None, 'https://painsolutionsaz.com', None, None, None, None, None, 'http://www.professionaldrivingschoolnc.com', None, None, None, None, None, None, 'http://www.sherwin-williams.com/store-locator/paint-store/Henderson/KY/1193', None, 'http://www.kerryscarcare.com', '1592273618', None, None, None, 'http://www.heroburgers.com', None, None, None, 'http://www.goldsgym.com', None, None, 'http://www.littlecaesars.ca/Locations/tabid/89/Default.aspx?id=NDcwMzAwMjc%3D&location=L1V+1A6%2CCanada', 'http://www.remadwindowrepair.com', 'http://www.rttheatingandcooling.com', None, 'http://heirloomphotostudio.com', 'http://www.harmonyhc.com', None, 'https://qdromasters.com', None, 'http://www.groutdoctor.com/locations/scottsdale-paradise-valley-az', None, 'http://www.norwoodinnhudson.com', None, 'http://www.alramzan.ca', None, None, 'http://www.luciemedispa.com', None, 'http://madeinmexicorestaurant.com', None, 'http://www.chianticafe.ca', None, None, 'http://www.postboxexpress.com', 'http://www.shininglightprenatal.com/', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'https://www.air72.com', 'http://mesafivestarcarwash.com', None, None, None, None, 'http://www.duffsfamouswings.ca/', 'https://www.omegawatches.com/en-us/store/storedetails/6709', None, 'http://www.troonnorthgolf.com', None, 'https://matthewsfun.org/OurParks/StumptownPark/tabid/182/Default.aspx', 'http://www.extremepita.com/', None, 'http://www.churchillspubandgrill.com', 'http://www.ramenlv.com', None, 'http://www.onelakewood.com/parks/', 'http://www.azfriends.org', 'http://www.dunkindonuts.com', None, None, None, None, None, 'http://www.canadarobotix.com/', None, None, None, None, 'http://www.lapazbatchoy.ca', None, 'http://www.dogeden.com', None, None, 'http://www.macayo.com/location/mesa/', None, 'http://www.smashbooth.net', None, 'http://www.humankanvas.com', 'https://locations.eatandys.com/ll/US/AZ/Mesa/1353-E-McKellips-Rd', None, 'http://mcbonies.com/', 'http://minimod.ca', None, 'http://www.foundryconcertclub.com', '1592273760', 'http://www.adamseaves.com', None, None, 'https://www.metro.ca/en/find-a-grocery/317', 'http://livingwaterlv.com/', 'http://estherneptune.com/', 'http://www.performanceone.net', None, None, 'http://www.alexandermcqueen.com', '1592273779', None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-deer-valley?utm_source=yelp&utm_medium=local&utm_campaign=Honorhealth_Medical_Group_Deer_Valley', 'http://www.saxbyscoffeeworldwide.com/', 'http://www.alterationsetc.net', None, 'http://www.goldminetavern.com', None, 'http://furniturefactoryusa.com', 'http://prod.getmymeal.com/en/asiandiningphoenix/', 'https://myrosatis.com/cavecreek/', None, None, 'http://www.premierwomenshealth.org', None, 'http://krasasalontremont.com/', 'http://www.ultimatewash.com', 'http://www.uncc.edu', None, 'http://www.barefootremedies.com', None, 'http://www.guyspizzaco.com', 'http://www.youngsbarbershop.com', 'http://paylessplumbercharlotte.com/', '1592273820', 'http://www.segar.ca', None, None, 'http://www.superiorNV.com', '1592273827', 'http://www.nothingbutbathrooms.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://zangautobody.com', None, 'http://www.rivermere.com', None, 'http://www.jtalleymd.com', 'https://tokojapanesesteakhouse.com', 'http://www.fallsoralsurgery.com', None, None, 'http://www.onceuponachildpineville.com', None, None, None, None, None, None, 'http://www.fieldfitgym.com', None, 'http://www.bhumikas.ca', 'http://www.allendrain.com/', 'https://www.backfithealth.com', None, None, '1592273874', 'http://firstaztitle.com', None, 'http://www.tractorsupply.com', 'http://www.802beancompany.com', None, 'http://www.lilicafepgh.com', None, 'http://www.flybouldercity.com/?q=contact', 'http://envisioncabinetryllc.com', 'http://www.healingsourcepharmacy.ca', 'https://www.rflaw.net', 'http://www.pittsburghdiamonds.com', None, 'http://www.yogaenergylv.com', 'http://www.baskinrobbins.ca', 'http://www.claytonkendall.com', None, 'http://www.bk.com', None, 'http://wanderingdonkey.com', 'http://www.blumenthalcancercenter.org', None, 'https://www.spengaphoenix.com', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=3365', None, 'http://luxuryeventcenter.net', None, None, None, 'http://www.srpnet.com/water/canals/recreation.aspx', '1592273925', 'https://www.ziggyspizzaphx.com', None, 'http://gold-needle-alterations.business.site', 'http://tavora.ca', 'http://thebrogue.ca', 'http://www.MattressOutletUSA.com', None, None, None, 'http://www.cubesmart.com/arizona-self-storage/gilbert-self-storage/2937.html', None, 'http://weolive.com/avondale/', None, 'http://www.tidedrycleaners.com', 'https://kitchencharmcookware.com/?utm_campaign=consumeraffairs&utm_medium=link&utm_source=ca-profile', None, 'http://jicky-jack-dba-jjs-bar-and-billiards-under-new.business.site', None, None, 'http://www.imagesbyedi.com/', None, 'http://www.ilovechurros.com', None, 'http://www.thewrendanforth.com/', None, 'http://www.firstoptionlandscape.com', 'http://www.cherokeetrailerrepair.com', 'http://www.southwestremarketingaz.com', None, None, 'http://www.mac-a-tak.com', None, 'https://www.madisonmarquettehotel.com', None, None, None, 'http://www.joesbuffetpalace.com', 'https://baizmarket.com', 'http://www.godiva.com', None, 'https://www.busterrhinos.com', None, 'http://www.mrosmow.com', 'https://www.nugateau.com', None, 'http://www.porkonaforkcatering.com', None, None, 'http://www.milestonesrestaurants.com/', None, None, None, None, '1592274019', 'https://locations.monro.com/pa/pleasant-hills/580-clairton-boulevard-route-51?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.greendoorlv.com', 'https://www.cobratireandautoservice.com', 'http://www.bullseyepaintingcompany.com', None, 'http://www.therealbarbershophenderson.com', 'https://stansclublamark.com', 'https://shop.beachtoyz.ca', None, '1592274043', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=1155', None, None, 'http://www.downtowntempe.com', None, 'http://www.lustforlashes.com', 'http://www.ndepthscuba.com', None, None, 'http://www.beckcenter.org/', 'http://www.fuzzystacoshop.com', None, None, 'http://www.appliancemedicclt.com/home.html', 'http://www.lasvegasoddities.com', '1592274074', None, 'http://salonutopialkn.com/', 'https://www.thecoreinstitute.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.barknbabies.com', None, None, None, None, 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', 'http://www.sweetflourpots.com/', None, '1592274096', 'https://greenzebrakitchen.com', 'https://t3.massagetherapy.com', '1592274103', "https://www.independentcitymarket.ca//store-locator/Mike's+Independent+City+Market+Toronto/2660", 'http://www.extremething.com/gen_info.htm', 'http://silverfernaz.com', 'http://galleriafamilydental.com', 'http://www.orchidthaifusion.com', 'https://www.HallLegalServices.com', 'http://www.wjkellar.com', None, None, 'http://www.taipantours.com', None, None, None, None, 'http://www.scottsdaleaz.gov/court', None, 'http://twistedburger.ca', None, None, 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', 'http://www.boostmobile.com/', None, None, 'https://cherrydowns.clublink.ca', None, None, 'http://www.paladinss.com', 'http://www.aubonpain.com', 'http://www.brookfieldplacenewsandevents.com', 'http://www.jtown.ca', None, None, None, None, 'http://www.azscience.org', None, None, 'https://www.tempeazchiropractor.com', None, None, None, None, 'http://qcteabar.com', None, '1592274172', None, 'http://www.cornerstonedentalaz.com', 'http://duranpestcontrol.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://beetjar.com/', 'https://batlgrounds.com/axe-throwing-scottsdale/?utm_source=Yelp&utm_medium=cpc&utm_campaign=2020&utm_term=scottsdale&utm_content=yelp-scottsdale', None, None, None, 'http://www.encoautotrimandglass.com/', 'http://www.fishellscreens.com/index.html', 'https://local.albertsons.com/az/scottsdale/6965-n-hayden-rd.html', 'http://www.bukharagrill.ca', 'http://www.barbeefarms.net', None, 'http://www.hauntedhillshayride.com', None, 'https://www.kleinsflowershop.net/?srccode=yelp_track', 'http://www.environmentalpest.com', 'http://www.bankofamerica.com', None, 'http://www.brownieconnection.com', None, 'http://www.mmtc.ca', 'http://www.fujiminc.com', 'http://ecospacanada.com/', 'http://www.zenrentpm.com', None, 'http://hendersoneventsplaza.com', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.whatabagel.com', 'http://www.phoenixperinatalassociates.com/', None, None, None, None, 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'http://www.a1garagedoor.ca/', 'http://bk.com/', None, None, 'http://www.menchies.com', None, None, 'http://www.amberalyseevents.com', None, None, None, None, None, 'http://www.hawkeyeengraving.com/', 'http://www.myrosatis.com/store-details/Mesa%20Greenfield', 'https://www.bmoharris.com', 'https://www.championwindow.com/Pittsburgh/?lpc=UU-OD-Pittsburgh-Yelp&source=ol-yel01&utm_source=yelp&utm_medium=local&utm_campaign=Pittsburgh', None, None, 'http://schustercompany.com', None, None, 'https://www.cslplasma.com/locations/bonuscoupon1216/91/donation-center-1334-e-broadway-102-tempe-az', 'http://www.autorepairtechnology.net', 'http://www.achildsplaceattheranches.com/', 'http://www.fitness14.com', 'http://davidsonmings.wix.com/mings-sushi', None, 'http://www.muchoburrito.com/', None, 'http://www.proswingz.com', '1592274289', 'https://www.kidsdentalsafari.net', 'http://KabutoKennel.com', 'http://ambiance.com', None, 'http://locations.michaels.com/nc/charlotte/5032/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.barrocoexpress.com', None, None, 'https://leos49.com', None, '1592274308', 'http://www.DesertDentalSpecialists.com', 'http://saddlemountainbrewing.com/', 'http://www.thestrathconahotel.com/dining', None, None, None, None, None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700006430792752&ds_s_kwgid=58700000444978432&ds_url_v=2', 'http://www.valleyincome.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://tripleserviceauto.com', 'http://academymortgageaz.com/chandler-branch/', None, 'https://www.nofrills.ca/store-locator/Tom%27s+nofrills+%28Bayly+St.+W.%29/1350?storeId=1350', None, 'http://www.vipsmartstorage.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.maxi.ca//store-locator/Maxi+%26+Cie+Pte-Claire+-+Nouveau%21+Le+magasinage+en+ligne+est+maintenant+disponible/8995?storeId=8995', 'https://www.unlimitedbrakes.com', None, None, 'http://essencehairajax.com', None, None, 'http://jpplatinumdetailing.com', 'http://www.hapsbbq.com', 'http://pizzahut.com/?utm_source=yelp&utm_medium=social&utm_campaign=enhanced%20yelp', 'https://locations.eatandys.com/ll/US/NC/Waxhaw/9921-Rea-Rd', None, 'https://www.supercuts.com/locations/pa/pittsburgh/shadyside-plaza-s-highland-haircuts-8953.html', 'http://powerwritersusa.com', None, None, 'http://www.aocphysicians.com', 'http://www.mesabathtubs.com', None, None, None, None, 'https://gem-theatre.com', 'http://www.alterrapest.com', None, None, None, 'http://louisgrill.com', 'http://www.renewedskinandbody.com', None, 'http://www.redpathsugars.com', 'http://www.clarkcountynv.gov/depts/fire/pages/default.aspx', None, None, 'http://www.ScottsdaleHillsAH.com', None, None, 'http://www.ranchmans.com', None, 'http://www.glenmorevisioncenter.com/', 'https://www.scottsdalepbs.com', None, None, 'http://www.preferredhomecare.com', None, 'http://www.penskeracingmuseum.com', 'http://chiropracticdelsol.com', 'https://www.farmersagent.com/cmikos', None, None, None, 'http://www.marriott.com/hotels/travel/clewb-courtyard-cleveland-willoughby/', 'http://www.olmtowing.com/', 'http://www.romeospizza.com', 'http://www.cheddardogs.ca', None, None, 'http://www.wrct.org', None, 'http://locations.harristeeter.com/sc/fort-mill/82/', None, 'http://westerndestinations.com/index.html#1', 'https://www.camelbacklincoln.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'https://www.gymboreeclasses.com/en/locations/ON/Thornhill/?utm_source=Yelp&utm_medium=website&utm_campaign=Thornhill&utm_content=yelp+page', 'http://eathotwok.com', 'http://sticklersaz.com/', None, 'http://www.anthonyjrs.com', 'https://wasabiexpressfairview.com', 'http://frglv.com/property/wayfarer-bar/', None, None, None, None, None, 'http://www.hotelalma.ca/', '1592274470', None, 'http://ad.doubleclick.net/clk;280858233;107462680;i', 'http://www.automotiondetails.com', '1592274476', None, None, 'http://locations.michaels.com/OH/MAYFIELD-HEIGHTS/5811/', 'http://www.targetsportscanada.com', None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, None, '1592274494', 'http://www.citybankantiques.com', 'http://stores.dickssportinggoods.com/nc/university/200/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, None, 'https://www.sprint.com/storefronts/bd/sprint-phoenix-az-85022-fcs-1908/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://lovesmovingcompany.com', None, 'http://mondoristorante.ca', None, 'http://www.glakeshonda.com', 'https://www.mattressfirm.com/stores/pa/pittsburgh/mattress-stores-pittsburgh-pa-15275-6433.html', 'http://www.renaissancepersonnel.com', None, 'http://raisingcanes.com', None, '1592274525', None, None, 'http://www.number1sound.com', 'http://www.northcoastwineclub.net', None, None, None, None, None, 'http://www.sallybeauty.com', 'http://rminteriorsanddesign.com', 'http://www.steelhousepittsburgh.com/', 'http://www.skinnypetes.com', 'http://www.clementemuseum.com/', 'http://www.richiifinecuisine.com', None, 'http://www.cafemonte.net/', 'http://www.ultramaticsleep.com/', 'http://www.bluejays.com', None, 'http://www.thedrafthouse.ca', '1592274563', 'https://www.sprouts.com/stores/details/-/store-details/view/store/501/?utm_source=yelp&utm_medium=listing&utm_campaign=website', None, 'http://www.affordableautoclinic.com/', 'https://www.staples.com', 'http://www.lagotremont.com', 'http://www.carters.com/home?id=carters&cm_mmc=Retail-_-Carters-_-Yelp-_-April', 'https://www.redmountainweightloss.com/gilbert/', 'http://www.kfc.com/storelocator/Default.aspx?address=2023%20E%20Lake%20Mead%20Blvd,North%20Las%20Vegas,NV', 'https://pekarabakery.com', 'http://www.pizzadelarte.ca', None, 'http://www.drfeli.com', 'https://arcadiapremium.com/', 'http://www.pilotdelivers.com/', 'http://www.vedatakeout.com', 'https://www.redroof.com/property/il/champaign/RRI170', None, None, '1592274601', None, None, None, 'http://abbotts.com/', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', None, 'http://www.ppcp.org/index.php/locations/bridgeville', None, 'http://kingandilv.com', None, 'http://www.marashicecream.net', None, None, None, None, None, 'http://www.reliablelocksmithing.com', None, 'http://www.calicocreekstables.com/', None, None, None, None, '1592274633', 'https://www.biltmoreloanandjewelry.com/not-your-average-pawn-shop-in-chandler/', 'http://mymarathonstation.com/StoreHome/56689', None, 'https://www1.shoppersdrugmart.ca', 'http://trekwestphoenix.com/', 'http://www.highlinemotorsportsaz.com', None, None, None, 'http://www.universalwindowslasvegas.com', 'http://arizonapestcontrolexterminators.com', 'http://www.auldspot.ca', 'http://www.peppinogourmet.com/', None, None, 'http://lindaslittleangelsphx.com', 'http://www.sobyboydenlenz.com/', 'http://www.greatamericancookies.com', None, 'http://stansburysbarbershop.tripod.com', 'http://ArizonaOncology.com', 'http://www3.ttc.ca/Routes/61/RouteDescription.jsp?tabName=route', 'http://www.alsmeatmarketanditaliandeli.com', 'http://www.bridgevilleautosales.com', None, None, None, None, None, 'http://www.mrhero.com', None, 'http://www.autobell.com/ab_locations/204-s-polk-st/', None, 'http://www.communitytoolchest.com', 'https://castileroofing.com', None, 'http://www.victoryservices.com', None, 'http://www.laeast.net', 'http://www.stardogcharlotte.com', None, 'https://www.pgatoursuperstore.com', 'http://www.vistek.ca', 'http://yogurtrocks.com', 'http://www.raywal.com/', None, 'http://www.vervewellness.com', None, None, None, None, 'http://www.deltaco.com', None, 'http://your-mail.ca', None, 'http://www.gotsmiledentistry.com', None, 'http://parrybros.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCAP', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://shamrocktowingaz.com', None, '1592274751', 'http://www3.hilton.com/en/hotels/arizona/hilton-phoenix-mesa-MESHPHF/index.html?SEO_id=YELP-HI-MESHPHF', None, None, None, None, None, None, 'http://www.funlfun.com/', 'http://www.burritozone.ca', 'http://www.eyecarenorth.com/', 'https://local.lenscrafters.ca/on/mississauga/100-city-centre-dr.html', None, 'http://cashbackaz.com', '1592274775', 'http://www.jiffylube.com', 'http://www.tylerberleen.com', 'http://www.valuevillage.com', 'https://www.dividedvine.com', None, 'https://haircutmen701shoppesmadisonwi.com', 'http://www.ftfcenters.com', None, None, 'http://www.mdlgroup.com', 'http://bowlbrunswick.com', None, 'http://www.granitetransformations.com/calgary/', 'http://www.deserthandtherapy.com', 'https://generalparts.com/location/phoenix/', 'http://www.mrsrobinsontoronto.com', None, 'https://locations.theupsstore.com/az/mesa/2753-e-broadway-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'https://www.restorationhardware.com/store-locations/store.jsp?storeId=157', 'http://www.cappitoffentertainment.com', None, 'http://www.vcahospitals.com/york-royalton?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_York_Royalton_Animal_Hospital&utm_campaign=main_url', None, 'https://www.gienow.com', 'https://locations.theupsstore.com/az/mesa/2753-e-broadway-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.holeinthewallgang.biz', 'https://seldensmiles.com', None, 'http://www.gretasolomonsdiningroom.com', 'https://www.theclassykitchen.com', None, 'http://knifetoronto.com', None, None, 'https://www.idealimage.com/medspa-locations/arizona/phoenix-area/phoenixchandler', 'http://www.harveys.ca', None, None, 'http://www.vinestyles.ca', 'https://www.budget.com/en/locations/us/wi/madison/m7n', None, 'http://maggiesfarmrum.com/', 'http://ananthabhavan.jimdo.com/', None, 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', 'http://www.thesteerandwheel.com/', None, None, 'http://www.chairrent.com', None, 'https://www.smithsfoodanddrug.com/stores/details/706/00370', None, None, None, None, 'http://www.1stcb.com', 'http://www.mkhbeauty.com', None, 'http://www.electronicsflip.com', 'http://www.ashworthlaw.com', None, None, 'http://www.sanealcamera.com', None, 'http://www.quiznos.com/', None, None, None, None, 'http://www.mooncongee.com', None, None, None, 'http://www.southpointetoyota.com/', 'http://www.bankofamerica.com', None, 'http://ItsABreezeRealEstate.Com', 'http://www.royfossthornhill.com/', None, None, 'http://www.rogers.com', 'https://www.qchiropractic.com', None, 'http://www.abridesdesign.com', None, '1592274920', 'https://renulasvegas.com', None, None, 'http://perfectteethandgums.com', None, 'https://www.pendleton-usa.com', None, 'http://pnc.com', 'http://www.carpetandrugsuperstore.com', 'http://rainbowshops.com', 'http://www.hellenikgrill.com/', None, None, 'http://www.toysrus.com/shop/index.jsp?categoryId=2255957', None, None, None, None, None, None, None, None, None, 'http://awagandawiggle.com/ProductsServices.aspx', None, 'http://www.azjunkremoval.com', 'http://www.tradermarcs.com', 'http://www.johnsonbank.com', None, None, 'http://www.mochajoes.net', None, 'http://dentalcareatmillscrossing.com', 'http://ilenestuxgown.com/', None, 'http://www.hookahlounge.com/', None, None, 'http://www.soma.com/store/home.jsp?cmp=MOC_yelp', None, None, None, 'http://www.abvilasvegas.com/', None, 'https://www.westerndental.com/en-us/find-a-location/arizona/phoenix/13651-n-35th-ave', 'http://ronsbereaautoservice.vpweb.com/default.html', 'http://www.salonandthecity.com', None, None, None, None, 'https://westtownmononatire.com', 'http://www.campusvacations.com/', 'http://prettykittywax.com/', None, 'https://order.subway.com/Default.aspx', 'https://www.westgateresorts.com/hotels/nevada/las-vegas/westgate-las-vegas-resort-casino/dining/sushi/', 'https://www.hilton.com/en/hotels/cleomhx-hampton-north-olmsted-cleveland-airport/?SEO_id=YELP-HP-CLEOMHX', 'http://www.thelodgetavernsvegas.com/cactus/', None, 'http://www.butcherandtherye.com/', None, 'http://www.sushishop.com/', None, 'http://www.foothillsfloral.co/', 'http://www.binions.com', None, 'http://www.u-swirl.com', None, 'http://Www.carolinacraftbutchery.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', None, 'http://4lakesdrivingschool.com/', None, None, 'https://www.enterprise.com/en/car-rental/locations/us/oh/parma-broadview-rd-3909.html?mcid=iyp:8368400', 'http://www.antiquealleync.com', None, None, None, 'https://kitanosushi.com', None, 'http://www.ho-chunkgaming.com/madison/', None, None, 'http://fiv5starhousecleaning.com', 'http://www.pooperscoopin.com/', 'http://www.redapronbakeshop.com', 'http://www.rossstores.com', None, 'http://www.sammysbeachbarandgrill.com', None, '1592275066', 'http://www.bravoitalian.com/northlake_mall.html', 'http://www.marriott.com/hotels/travel/pitrn-residence-inn-pittsb', 'https://locations.levi.com/az/glendale/denim_glendale_az_248.html', '1592275076', None, 'http://28thstreetautorepair.com/', '1592275081', '1592275084', 'http://www.istarrestaurant.com/', None, None, 'http://fusiadog.com', None, 'http://www.harrahs.com/casinos/caesars-palace/restaurants-dining/neros-detail.html', 'http://FedericosMexicanFood.com/', 'http://www.awayhomemoving.com', None, None, 'http://www.mikesgrowersoutlet.com', 'https://www.kohls.com/stores/nv/henderson-1364.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.sunriseseniorliving.com/communities/sunrise-of-chandler/overview.aspx?&xid=10000240&utm_source=yelp&utm_medium=online_review&utm_campaign=Yelp%20_CTA_Generic%20&utm_term=lead_nurturing&utm_content=Learn_More_Website', 'http://www.kernsplumbing.com', 'http://www.aptfind.com', None, '1592275116', 'http://www.ichibansushi.com', 'http://www.indianparadiseaz.com/', 'https://www.craftaptsaz.com', 'http://www.biscuitscafe.com', None, 'http://www.plumpanasiankitchen.com', None, None, None, 'http://www.cucinaoliveoil.com', 'http://www.golftheoaks.com', None, None, 'http://www.bk.com', None, None, 'https://www.integrasprings.com', None, 'http://www.gonzaloslandscaping.com', None, 'http://www.thewoodshedbar.com', None, None, 'http://www.coachworksautobody.com', 'http://www.ashleystowing.com', None, 'https://www.homegoods.com/store-details/Las-Vegas-NV-89149/312', 'http://www.happyfeetreflexologyaz.com', None, None, 'http://www.macys.com', None, 'http://www.onesbetterliving.com', None, '1592275175', 'http://www.cclonemountain.org', 'http://malibucleans.com', 'https://www.aqua-tots.com/mississauga-east/', None, 'http://craigmuellerlaw.com', 'http://www.samthedogtrainer.com', None, 'http://www.vittoriosbuonappetito.com', None, None, 'https://www.gianttiger.com/store-locator/giant+tiger+%23152.do', None, None, 'http://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXFA', None, None, 'http://www.ugpillinoisapparel.com', 'http://www.swiftkeylocksmith.com', 'https://www.goddardschool.com/cleveland/concord-township-fredle-road-oh?utm_source=yelp&utm_medium=business_listings&utm_campaign=school&utm_content=main_button', None, None, 'http://bandierajewellers.com', None, 'http://www.onesbetterliving.com', None, 'http://torontocondos.com/', None, 'http://deansadlerphoto.com', None, None, 'http://www.sevennumbers.com', None, 'http://www.snowcity.com', 'http://artisanalfoods.com', '1592275233', None, 'http://bk.com/', None, 'https://shawarmavegasgrill.com', None, None, None, None, '1592275249', 'http://www.harborfreight.com', None, None, None, 'http://www.Lamsmarket.com', None, None, None, 'http://www.wolfgangsonbrock.ca', 'https://www.chick-fil-a.com/universityatmill', 'http://www.chapters.indigo.ca', None, None, 'http://www.maidempire.com', 'https://www.cafeandmi.com', 'http://www.vietnamesephogrill.com', 'http://www.culturepgh.com', None, 'https://www.8main.ca/pages/toronto', None, 'http://WWW.Allabouttennis.com', None, None, None, 'http://www.detailboysllc.com', 'http://www.aussierulescalgary.com', 'https://www.summitcreditunion.com/fitchburg', None, '1592275299', None, 'http://www.ThomasGonda.com', None, 'https://www.roofroofnc.com/?force_source=local_organic', 'http://www.alwaysrunningrepair.com/', None, 'http://shoerepairsonline.com', 'http://www.boxgrovedental.com', None, 'http://www.cobblersdenaz.com', None, 'http://www.lvmobilemechanic.com', None, 'http://nocrunchycookies.com', 'https://www.macaronigrill.com/locations/location?id=229', None, 'https://stores.joann.com/wi/madison/319/', 'https://www.goodwill.ab.ca/goodwill-location/chinook/', 'http://www.yogafactory.com', None, '1592275343', None, None, 'http://www.parktavernbar.com/', None, 'http://www.italiangrotto.com', None, None, None, 'http://lukesofchicago.com/', None, None, 'http://www.madisonstaybridge.com', None, 'http://www.babybloomnutrition.com', None, 'http://www.dancexcelstudio.com/', 'https://ericsolbergdds.com', None, 'http://phoenixappliancetech.com', None, None, 'https://eatletao.com', None, 'http://www.gentledentalwestchandler.com', None, 'http://enchantedpoutinerie.com', None, 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', 'https://locations.churchs.com/az-surprise-10339', 'http://www.adl-solutions.com', None, None, 'http://www.thegamecrafter.com', 'http://www.arnoldsteapittsburgh.com', 'https://thealpacaboutique.com', 'http://www.ruthschrislasvegas.com', 'http://www.jencormortgage.com', None, 'http://www.hurmlawfirm.com', None, 'http://www.aztintguy.com', 'http://www.lavikkaphotography.com', None, 'http://paulsneighborhoodbar.com/', 'https://www.palacestation.com/eat-and-drink/little-tonys/', None, 'http://lifestreamwellnessclinic.com', None, '1592275433', None, None, 'http://www.bellalunaaz.com/', 'http://billiardfactory.com?utm_source=yelp&utm_medium=directory&utm_campaign=las%20vegas', 'http://fahmeebakery.com', 'http://www.bellissimosalonandspa.com/', 'http://www.thebutcherblocklv.com', None, None, None, 'http://www.servicecanada.gc.ca/tbsc-fsco/sc-dsp.jsp?lang=eng&rc=4802', 'https://www.uwhealth.org/locations/clinic_detail.jsp?sublocationId=769', 'http://www.boarnwing.com/', 'https://www.kernelspopcorn.com', 'http://www.mesa-dental.com', None, 'https://majerles.com/locations/downtown/', 'http://reeldentalaz.com/', None, 'http://www.novusglass.com/locations/las-vegas/en/', None, 'http://www.townandcountryford.com', 'http://michelleclarkphotography.com', None, None, None, None, None, None, 'http://www.valueplace.com/', None, 'https://littlecaesars.ca/en-ca/stores/48600201/3100-winston-churchill-blvd/mississauga/on/contact', 'http://tandinhrestaurant.com/', None, 'http://indianrotihouse.com', None, 'http://www.timhortons.com', None, 'http://www.haulin-goats.com', 'http://www.themutthutt.com', 'http://www.sleepwelllasvegas.com', None, 'http://www.massage-marketing-solutions.com/las-vegas-massage.html', 'http://www.chapters.indigo.ca', 'http://www.thebosstaxi.com', None, None, None, None, 'http://belzycki.ca', 'http://www.dfdentistry.com', '1592275533', 'http://www.wahlheatingandcooling.com', 'http://www.humana.com', None, None, None, 'https://www.azentsurgery.com', 'http://centurycommunities.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, None, None, None, 'http://www.unionvet.ca', 'http://arorachiropractic.com', '1592275560', 'http://www.phillyfreezeme.com', 'http://www.bcbg.com', None, 'http://treeremovalsurpriseaz.com', 'http://www.fxfitnessclubs.com/willoughby', 'http://www.uncorkthefun.com/charlotte-north-carolina/site-info', None, 'http://www.upholsterycleaningcharlotte.com', 'https://complexneurology.com', 'http://www.desertwillowconferencecenter.com', 'http://www.coachusa.com/lenzner/', None, 'http://www.theparamountapts.com/', 'http://www.calvinklein.com', None, 'http://www.makeupenhancements.com', 'https://www.americancampus.com/student-apartments/il/champaign/309-green', None, None, None, None, None, 'http://www.mtcfactoryoutlet.com', None, 'https://locations.panerabread.com/oh/broadview-heights/2000-e-edgerton-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://treesoftomorrowtrimmingservices.com', 'https://www.maricopa.gov/Facilities/Facility/Details/East-Valley-3', 'https://www.peterpiperpizza.com/locations/avondale-az/cold-water-plaza', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Madison-WI-53714/749051/', None, None, None, None, None, None, None, None, None, 'http://www.subway.ca', None, None, 'http://mastertacoaz.com/contact/', 'http://pawpals.ca', 'http://www.landscaper-phoenix.com', None, 'http://www.azbesttire.com', 'http://www.uli.com/', None, None, 'http://www.riversidemarinanc.com', None, 'http://bashaverdun.ca', 'http://www.deltaco.com', 'http://www.heritageamusementrides.com', None, None, 'http://www.goldmedalswimschool.com/', None, None, None, '1592275655', None, 'http://www.whichwich.com/', 'http://gojisyogurt.com', 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=555', 'https://www.maricopa.gov/797/Planning-Development', 'http://www.federickrestaurant.com', None, None, None, None, None, None, None, None, None, 'http://www.kingtandoori.com', 'http://mississauga.indiastaste.ca', None, None, 'http://blokeand4th.com', None, 'http://www.buffalowingsandrings.com', 'http://pickupstix.com', 'http://andelemexicanrestaurant.com', 'http://rayaspizzeria.com', 'https://www.costco.ca/warehouse-locations/downsview-north-york-on-535.html', None, None, None, None, None, 'http://lavanderiaresto.com', None, None, None, None, 'http://www.aswlv.com', 'http://www.buffalowildwings.com', None, 'http://www.totopizza.com', None, 'http://www.rosemanmedicalgroup.com', None, None, None, None, None, 'https://www.riteaid.com/store-details?storeNumber=11467', None, 'http://www.uppervillagedental.com', 'http://www.sushi2go.ca', 'http://www.caprettiandco.com/', None, '1592275733', 'https://www.chandlerdentalarts.com', 'http://www.greyhawkgolf.com', 'https://www.staples.com', 'http://www.illbeseeingyou.ca', 'http://www.fiveguys.com/', None, None, 'http://www.costco.com', 'https://www.brattonconstructionaz.com', None, None, None, 'http://www.412brews.com/contact.html', None, 'http://www.familymemoriesnc.com', 'http://www.boxdropfurniture.com', 'http://www.super5toronto.com', None, 'http://myfroyotwist.com/', None, 'http://www.joyclean.vpweb.com', None, None, None, 'https://locations.theupsstore.com/sc/fort-mill/9789-charlotte-hwy?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.epicnails702.com', 'http://theberlinerlv.com/', 'http://www.sav-onplating.com', None, 'http://www.meadowvalehonda.ca', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.asecretgarden-floral.com', '1592275799', 'http://www.chefmarcstrattoria.com', None, None, 'http://www.waxyboutique.com/', 'http://ultraskinwaxcenter.com', 'https://www.singhsmilecare.com', None, 'http://m2medicalspa.com', None, None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, None, 'http://www.idsincnv.com/', None, 'https://locations.panerabread.com/pa/oakmont/666-allegheny-river-blvd.html', 'http://elevatedtoronto.ca', None, None, 'http://www.metropointmedia.com', None, 'http://atriumframing.com', 'http://www.freshcutsphoenix.com', 'http://www.quiktrip.com', None, 'http://www.barmercurio.com', 'http://www.azperio.com', 'http://www.rejuvenate4u.com', 'http://www.olesiasplace.com', 'http://taffetaandtulle.com/', None, None, None, None, None, None, None, None, 'http://www.donthecarcareman.com', 'http://www.3800lux.com', None, 'https://www.bonefishgrill.com/locations/nc/matthews-charlotte', 'https://discountrocksandandgravel.com', None, None, 'http://www.titojimy.com', 'http://torontofoodtrucks.ca/sushiburri-toronto-food-truck', None, None, None, 'http://www.arizonapainrelief.com', 'http://www.zindiacatering.com', 'http://glendalehvacservice.com', None, None, None, None, 'http://www.chandleraz.gov/aquatics', 'https://www.nofrills.ca/store-locator/Pat%27s+nofrills+%28Wilson+Ave.%29/1330?storeId=1330', 'http://www.theperfectfitbridalboutique.com', '1592275898', None, 'http://www.crowleysfamilydentistry.com', None, 'http://www.littlecaesars.com/MobileLocations/tabid/483/location/44224/Default.aspx?id=MTU1ODAwMDU%3d', None, None, 'https://locations.churchs.com/az-phoenix-7235', None, 'http://www.montefiorecare.org', 'https://www.truliantfcu.org', 'http://www.calgaryplaza.com', None, None, 'http://www.anytimetantanningclub.com', 'http://www.futonsforless.ca', None, None, 'http://www.lush.ca', None, None, 'http://blueribbonfriedchicken.com/las-vegas-summerlin/', 'http://le-nailspa.com', None, None, 'http://www.buehlers.com', None, 'http://www.forthebirdsbyrobinhawk.com', 'http://www.thelittledollhousecompany.com/dollhouses-miniatures-furniture-kits/index.php', 'http://www.archapothecary.com', None, None, None, 'http://mejicoaz.com/', None, 'http://www.azbanners.com', None, 'https://hearusa.com', None, 'http://www.sunvalleyanimalhospitalnc.com', 'https://www.redstarvapor.com/stores/vape-shop-glendale-olive-ave/', 'http://carusohairsalon.com', 'http://www.madisonlaptoprepair.com', 'http://OrangeEquipment.com', 'https://familyurgentcare.com', None, 'http://www.momsfixins.com', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/calgary-3315-32nd-avenue-ne.aspx?storeid=12&code=pc', 'http://www.helixelectric.com', None, 'http://www.pumayoga.net/', 'http://whasn.com', 'http://www.theremyco.com', 'https://www.interdent.com/gentle-dental/locations/nv/henderson/653-n-stephanie-st-dentist-office?utm_medium=yext&utm_source=organic', 'https://cocofreshtea.ca', None, None, 'http://www.jtbobahouse.com/', 'http://www.eastsidemarios.com/', None, None, None, 'http://www.familydollar.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.rockhillauction.com', 'http://www.legumebistro.com', 'http://www.vccaz.com', None, 'http://www.balancedphysicaltherapy-pilates.com', None, 'http://www.downeastphotographers.com', None, 'http://www.carusoscoffee.com', 'https://www.performancebike.com/bike-shop/store/mayfieldheights?utm_campaign=yelp&utm_medium=organic+&utm_source=local', None, None, None, 'http://www.dominos.com', 'http://www.javastoptrolley.com', 'http://www.thelightcellar.ca', None, 'http://www.aeandsons.com/', None, 'http://www.bk.com', None, 'https://www.payless.com/stores-location/NV-LAS-VEGAS-5798.html', None, 'https://www.tileshop.com/store-locator/oakwood+village.do', None, 'http://kidzaam.wix.com/kidzaam', 'http://www.somethingclassic.com', 'http://washndrylaundry.com/', None, None, None, None, 'http://www.drjdental.com', 'http://www.gameremt.com', None, 'https://www.chabivegas.com', 'http://www.solarenergytan.com', 'http://www.tuninggruppe.com', None, 'http://www.theflamebbq.com', 'http://www.earthviewyoga.com', 'http://www.hakimoptical.ca/', 'http://www.sunprairieliquorstore.com', None, 'http://www.whiffwaff.ca', 'http://clickserve.dartsearch.net/link/click?lid=43700044282947182&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.gusspizza.ca', None, '1592276081', 'http://www.glassybusinesslv.com/', None, None, None, 'http://www.americasbest.com/?utm_source=yelp&utm_medium=textlink&utm_campaign=5551', 'http://www.redrockcanyonlv.org/hikes-trails/ice-box-canyon', 'http://www.evergreenwellnesscentre.weebly.com', 'http://www.climbnorth.com', 'https://locations.sonicdrivein.com/nv/lasvegas/6301-w.-lake-mead-blvd..html', 'https://phillypretzelfactory.com/locations/goodyear/', 'http://karshopaz.com', 'http://www.appletreetoronto.com', 'http://www.calgarylockandsafe.com', 'https://djsfitness.com', None, 'http://www.misspole.com', 'https://www.sagewoodlcs.com/health-services/acacia-health-center/', 'http://www.midas.com/toronto/store.aspx?shopnum=9105&dmanum=857001', None, 'http://www.bestlemongrass.com', 'http://www.thewestbury.co', None, 'http://www.eastsidemarios.com/locations/mississauga/ontario/mavis', None, None, None, 'http://gaianaturalfoods.ca', 'https://www.foamortgage.com/loan-officer/leroy-longsworth-921769/', None, None, 'http://www.charlotterunning.com/', 'https://nathansfamous.com/restaurants/luxorhotelcasino-lasvegas-130416/', None, None, None, None, 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', 'http://www.gorgeousglo.com', None, 'http://lebisoumedspa.com', 'http://www.habitatrestaurant.com', 'https://www.bungalowsonolive.com', None, None, '1592276164', None, None, 'http://www.goodwillaz.org', None, 'http://www.valencienne.com', None, None, '1592276176', None, None, 'http://www.charlesdavid.com', 'https://www.usps.com/', None, 'http://www.divanailssalon.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.sandwichbox.ca', None, None, None, None, None, None, 'http://locations.in-n-out.com/80', None, None, None, 'http://www.dav.org', 'http://www.findlaycustoms.com/', None, 'http://www.quiktrip.com', None, None, 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID155', 'http://www.mynextsalon.com', 'http://www.mistergroomingandgoods.com', None, 'http://www.calgarylaserhealth.com', 'http://www.crossfitinfernal.com/', None, None, None, None, 'https://www.papajohns.com', 'http://www.sunnyfootspa.ca/index.html', 'http://www.crossfitblur.com', 'http://www.frostedenvy.com', None, '1592276237', 'http://www.petitphilippe.com/', None, 'http://www.walkersridge-apts.com', None, None, None, None, None, None, None, 'http://7eleven.ca/store-locator/14812', '1592276258', None, 'https://www.classicjewellv.com', None, 'http://www.illinimattress.com', None, None, 'https://www.target.com/sl/charlotte-midtown/2244', '1592276267', 'http://www.empowermd.com', None, 'http://organic-hair-boutique.business.site', 'http://www.nessalla.com/', '1592276276', None, None, None, None, 'https://www1.shoppersdrugmart.ca', 'http://go.georgestreetphoto.com/l/9752/2014-06-04/m1c3p', None, 'http://www.summerlink.com', 'http://www.tradinglabels.com', 'http://www.heroburgers.com', 'http://www.atamijapanese.com', 'https://www.pharmaprodia.com', None, None, 'http://www.thechefupstairs.com', None, None, 'http://www.finishlinecarwash.biz', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1015+East+Ray+Road-Chandler-AZ-85225/storeid=7849?cid=ps_ylp_2020', 'http://hibachisteakhouse.ca', None, 'http://portofinos-us.com', None, None, 'https://www.mountainsideaz.com', None, 'http://www.scratchfoodbev.com', 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', 'http://www.merrillpestsolutions.com', 'http://www.nevadafloormasters.com', 'http://www.vehiclepurchasingservice.com', None, 'http://www.bayviewsheppardrmt.com', None, None, 'https://www.planetfitness.com/gyms/avon-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'https://www.sunsetgrill.ca', 'https://www.sonataapts.com', None, None, 'http://www.nobulltrees.com', None, None, None, None, None, None, None, 'http://www.lasenchiladasdemama.com', None, 'http://www.NiklasGroup.com', 'http://www.pjsflowers.com', 'http://www.zenergydogtraining.com', None, 'http://www.noappointmentmdaz.com', 'https://www.bannerhealth.com/locations/mesa/banner-children-s-specialists-3', 'http://www.palacestation.com/dining/pasta-cucina/', 'http://firenzapizza.com', 'http://judsbest.com/', None, 'https://www.southstburger.com/location/st-clair-rushton/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/7697+Charlotte+Highway-Indian+Land-SC-29707/storeid=5479?cid=ps_ylp_2020', None, 'http://www.landroversolon.com', 'http://www.vintagephotoboothrentals.com', 'http://www.regalrags.com', None, None, None, 'https://www.fitbodybootcamp.com/westchandlerfitnessbootcamp/', 'http://www.spalashesbysaundra.com', None, None, None, 'https://www.dianasblindsanddesigns.com', None, None, None, 'http://www.prometric.com', 'http://www.7-eleven.com/?yelp=29384', None, None, 'https://find.shell.com/us/fuel/10006254-808-s-priest-dr', None, None, 'http://www.17thstreetcafe.com', None, 'http://www.anaboutique.net', None, None, None, None, 'http://www.andreaspetsittingandboarding.com', None, 'http://www.publicbeermarket.com', None, 'http://lamannafashion.com', None, 'http://www.petco.com', 'https://la-bamba-mexican-grill-restaurant.negocio.site', None, None, None, 'http://preludesalon.ca/', '1592276449', None, None, 'http://scruplessalon.com', 'http://charmeck.org/mecklenburg/county/parkandrec/parks/parksbyregion/centralregion/pages/freedom.aspx', None, None, None, 'http://towncrierpub.ca/', 'http://www.76.com/station-finder', None, None, 'http://holidaypetcare.ca/', None, 'https://gamesuaz.com', 'https://stores.bestbuy.com/oh/elyria/6650-midway-blvd-284.html/?loc=ns100&ref=NS', None, None, 'http://www.metzinspection.com', 'https://www.apollorv.com/rv_rentals_locations-lasvegas.aspx', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.iaautomotive.com', 'http://www.pizzapatron.com', 'http://www.calicocorners.com/storepage.aspx?storeid=176', 'http://www.windowsareapane.com', 'http://www.tonpottery.com', 'http://www.meatballspot.com', 'http://www.citroncateringaz.com', None, None, None, None, 'http://www.gotransit.com/', 'http://www.charlottecitytennis.com', None, None, None, 'http://www.spasbydesign.com', None, 'http://deervalleyfamilydentistry.com/', None, None, 'https://myhoneybakedstore.com/phoenix/8702', 'http://www.bedbathandbeyond.com', 'http://www.bigcreekmassotherapy.com', None, 'https://www.spencerstv.com/locations/gilbert.html?utm_source=website%202711', 'http://www.creamandflutter.com', 'http://www.theharppub.ca/', None, 'http://www.thewhiningpig.com/', None, None, 'http://www.vanimalsanctuary.org', None, None, None, '1592276534', None, 'http://abbeyroadpub.ca', None, None, 'http://cravetempe.com/', 'http://www.glendaleciviccenter.com', None, None, 'http://www.superautosaleslv.com', 'http://www.waffluv.com/find-us', None, None, None, None, None, None, 'http://integritystaffing.com', None, 'https://www.triconamericanhomes.com', 'http://www.torontosurgery.com', 'http://www.citybarbersatuptown.com', None, 'http://www.eyebrowsrus.com', None, None, None, None, 'http://www.kingsbeerwine.com', None, None, 'http://thepubchipshop.com', 'http://www.ttc.ca', 'http://www.charlottepublicgolf.com', 'http://alleghenyarms.com', 'https://xoghwngml.wixsite.com/kbbq/', 'https://www.choicehotels.com/north-carolina/charlotte/quality-inn-hotels/nc511/rates', None, None, 'http://www.dilworthanimalhospital.com', 'https://www.truefoodkitchen.com/jubytrue', None, 'http://www.charlotterusse.com', None, 'http://www.cashmanbrothers.com/', 'http://Doors4Mutts.com', 'https://www.rmcf.com/AZ/Tempe50423', 'http://www.oakandivy.com', None, None, 'http://www.olivethis.com', 'http://www.stellcpa.com', None, 'http://villamadina.com', None, None, 'https://www.mandalaybay.com/en/nightlife/mizuya-lounge.html', None, 'https://www.fatburger.com/locations/rancho', None, None, 'http://www.yelp.com/events/tempe-real-wild-and-woody-indoor-craft-beer-festival', None, 'https://movatiathletic.com/fitness-clubs/richmond-hill/?utm_campaign=fy18annual&utm_medium=profilepage&utm_source=yelp&utm_content=septRCH', None, None, 'http://www.revitasize.ca', 'https://www.laoszechuanchampaign.com', None, 'http://brickstreetbakery.ca', None, None, 'https://www.fortcalgary.com', 'http://thegreataustralianbakery.com', None, None, 'http://www.metrocigar.ca', 'http://www.leavittsautocare.com/', 'https://atriumhealth.org/locations/atrium-health-steele-creek', 'http://nativegrillandwings.com/location/phoenix-tatum-bell/', 'http://sixshootercoffee.com', 'https://www.shopbotanistohio.com/wickliffe-location', 'http://www.aces-depot.com', 'http://nowshakrestaurant.ca', 'http://www.pennymacusa.com', None, None, 'http://thriftylv.com/', 'http://xtremeautoworksaz.com', None, None, None, 'http://www.schrefflercustomwoodflooring.com', 'http://www.alliantenergycenter.com', 'http://www.justgreek.ca', 'http://www.oasisurbancafe.com', None, 'https://www.customoutdoorliving.net', None, None, None, 'https://www.assistanceleague.org/find-a-chapter-or-thrift-shop/location-information/?id=0011a00000DzO62AAF', None, None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', None, 'http://www.molisanaitalianbakery.com', None, None, 'http://www.wheelycleanwash.com', None, 'http://locations.alfredangelo.com/pa/monroeville/aa033/', 'http://www.godiva.com', None, 'http://www.la-z-boy.com/Northeast-Ohio/Howe-Ave', None, 'https://www.rubytuesday.com/', None, 'http://www.knuckleheadspizzas.com', 'https://locations.theupsstore.com/az/glendale/20118-n-67th-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, None, 'http://www.parccentralrestaurants.com', 'http://reflectionsnv.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/ky/henderson-5842.html?mcid=iyp:8368400', 'http://theitaliancobbler.com/', None, None, None, 'http://www.tacodelmar.com/', None, 'https://www.sprint.com/storefronts/bd/sprint-north-olmsted-oh-44070-fcs-846/?ecid=SEO:Yelp:2020_Q1:LastMile', None, None, None, 'http://www.visioncareyorkville.com', 'http://www.speedyglass.ca/locations/markham/', None, 'http://www.nvjets.com', 'http://www.acrossarizonatours.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, 'https://surprisetowing.net', 'http://www.dollargeneral.com/home/index.jsp', 'http://www.stackskitchen.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.reafieldvillage-apts.com', None, 'http://www.canadarunningseries.com/sportinglife/sl10kDET.htm', 'http://www.lifehealthmassage.com', None, None, 'http://www.queondatacos.com', None, 'https://www.ediblearrangements.com/Stores/245-East-Bell-Rd-Phoenix-AZ-85022', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.openlotcars.com', None, 'http://www.newhopelasvegas.com', None, 'http://centraldentalcare.com', 'http://www.saporosushi.com', 'http://www.gnc.com', None, 'http://www.holtfamilydentistry.com', None, 'https://www.newgridpower.com', None, 'http://www.oshiropediatrics.com', 'http://www.cinnamoncalgary.ca', 'http://radioshack.com', None, None, 'http://www.beadjungle.com/', None, 'http://www.clarkcountycarpet.com/', None, None, None, 'http://forestparkphoenix.com/', None, None, 'http://www.ziarecords.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXAC', None, None, None, None, None, None, None, None, 'http://www.phoenixembroideredpoloshirt.com', None, None, None, 'http://www.centralchurchofgod.org', 'http://www.habitatgeauga.org/', 'http://locations.in-n-out.com/153', None, 'http://theabbot.ca', 'http://cuddlescaninespa.com', None, None, None, None, None, 'http://www.rileyspourhouse.com', None, None, '1592276863', None, 'http://www.sugarkanerestaurant.ca', 'https://www.tlcwings.com', '1592276872', None, 'http://madisonvaporstore.com/', None, 'https://www.performancebike.com/bike-shop/store/peoria?utm_source=local&utm_medium=organic%20&utm_campaign=yelp', 'http://www.pinevillagevet.com', 'http://www.pittsburghcomics.com', '1592276882', 'http://www.losarbolesapartments.com/', None, None, 'http://www.starbucks.com/store/17988/', 'http://www.bellavitamadison.com', 'http://niceguyzmoving.com', 'http://www.hillsong.com/phoenix', None, 'http://locations.harristeeter.com/nc/charlotte/205/', None, None, None, 'http://www.boehmer.ca', None, 'http://www.signaturedesserts.com', 'http://www.unlimitedsmiles.com/office-chandler.html', None, None, None, None, 'http://www.aurasmiledental.com', 'http://www.culvers.com/restaurants/deforest', None, 'http://cabinetstogo.com/store/cabinets-charlotte-nc', 'https://www.corepoweryoga.com/free-week?utm_source=yelp&utm_medium=cta&utm_campaign=paradise-valley-yelp-free-week', 'http://www.dearbornbaby.com', 'http://www.steakonastone.us/', None, None, None, None, None, None, None, 'http://blueberry-blessings-christian-bookstore.business.site', None, None, None, None, None, 'http://www.thesinobi.com', 'https://ad.doubleclick.net/ddm/clk/316235911;144466976;n', 'http://www.riversidegablesbb.com/', 'http://www.summeridgeanimalclinic.com/', None, 'https://www.spectrum.com/locations/oh/akron/1919-brittain-rd', 'http://www.arispt.com/', 'http://www.sterlingyoga.com', 'https://nathansfamous.com/restaurants/luxorhotelcasino-lasvegas-130416/', None, 'http://www.cutlerandgross.com', 'http://restyourash.com/', None, None, 'http://www.roadrunnerglassco.com', None, 'http://www.aliveafterfives.com/', 'http://carnegielibrary.org', None, 'https://www.fxrxinc.com/', 'https://www.ktxinsurancebrokers.ca', None, None, None, None, 'http://www.dekefir.ca', 'http://onaukmor.com/', 'http://pizzastudiocanada.com', None, None, None, 'http://www.smilelabsarizona.com', None, 'https://dutchbros.com/?utm_source=gilbert&utm_medium=yelp&utm_campaign=website_gilbert', None, None, None, '1592277002', 'https://deals.homejoy.com/exclusive?s=US_YEL_YEL&utm_source=US_YEL&utm_medium=YEL&utm_campaign=US_YEL_YEL_WSL_LO-YYZ+Toronto', 'http://www.excaliburautobody.com/', 'http://solarnailsandspa.ca', 'http://polisheats.com/', 'http://blackjackwindowtinting.com', None, 'http://www.sushihamarestaurant.com', None, 'http://stelviotoronto.ca', 'http://www.foodlion.com', None, 'http://www.vivachicken.com', None, None, None, None, None, None, 'http://ltgrill.com/', None, None, 'http://bomanite.ca/', None, None, None, None, '1592277047', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Toronto-ON-M6H2B5/059238/', 'http://www.loomshowroom.com', 'http://www.fortmcdowelldestination.com/anhala', 'http://www.mcdonalds.com', 'http://avis.com', None, None, None, None, 'https://www.saladamarket.com', 'http://www.partycakeshop.com/', None, None, 'https://importconnectionrepair.com', None, 'http://madison-west.orangeshoe.com/', 'http://www.mibcleaningservices.com', 'http://www.music49.com', 'http://www.biscuits2burgers.com', 'https://carolinadigestive.com/locations/pineville-office', None, 'http://bearcabinetry.com/', None, None, 'http://www.beautyintervention.com', None, 'http://www.clevelandimprov.com/', None, None, None, 'https://locations.churchs.com/az-phoenix-7235', None, 'http://chandler.newvalleychurch.org', 'https://www.amctheatres.com/movie-theatres/phoenix/amc-surprise-pointe-14?utm_uid=yelp', None, 'http://www.championpizza.com', None, 'https://www.quickhairbraiding.com', None, None, 'http://fergusandbix.com/', None, None, None, 'http://www.hands4hire.com', 'http://www.shiningstarsacademy.com', None, None, 'https://www.stanleysteemer.com/?utm_source=yelp&utm_medium=referral&utm_campaign=yelp_branch_ws_ad', None, None, None, 'http://www.ohioeyecareconsultants.com', 'http://www.19thdonuthole.com', None, 'http://jerusalem-shawarma.ca', 'http://www.cartwrightmotors.com', None, 'http://www.hosu.ca/', 'http://www.sephora.com', None, 'http://www.cherokeehillsgolf.com', 'http://www.fineartdecor.net', None, 'http://mayflowerlandscapingllc.com', 'http://www.stationskiandride.com', None, '1592277174', 'http://gilbertcenter.net/', None, 'http://www.yelp.com/events/charlotte-yelps-moonrise-brunch-tupelo-honey-cafe', None, None, None, 'http://budgettruck.com', 'http://stores.arcteryx.com/toronto', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, '1592277190', 'https://www.sprint.com/storefronts/bd/sprint-independence-oh-44131-d-4687/', '1592277194', None, 'http://www.asyouwishpottery.com/', 'http://giovannispizzaon5th.com', 'https://nationwidevision.com/locations', None, None, None, None, 'https://www.pacificdiner.org', None, 'http://www.romanfountain.com/', 'http://peoriacheerz.com', None, 'http://nvpeds.com/', 'https://order.subway.com/Default.aspx', 'http://www.carolescheesecake.ca', 'http://www.tedbaker.com/us/stores/store/70127', None, None, None, None, '1592277231', None, None, None, 'http://www.familydollar.com', 'http://www.level10audio.com', 'http://www.cirque-ability.com', None, None, 'http://www.thomasmertoncenter.org/', None, 'http://xplicitshowclub.com', 'https://www.choicehotels.com/arizona/peoria/ascend-hotels/az385/rates', None, 'http://www.juliasbridal.ca', 'http://cooperplumbing.com/index.php', None, None, None, 'http://www.torontowarriorsvolleyballclub.com', None, None, 'http://freshwestgrill.com/', 'http://www.westernreservewines.com', None, 'http://www.kidtokid.com/Paradisevalley', None, None, None, 'https://locations.wendys.com/united-states/nc/mint-hill/6849-matthews-mint-hill-rd.', 'https://pistachiobakeshop.ca', None, None, '1592277277', 'http://www.brockstreetbrewing.com', 'http://www.beanfieldcentre.com', 'http://www.sony.ca', None, None, None, 'https://haircutmennorthphoenixaz.com', None, None, None, 'http://www.drivepetty.com', 'http://thestrathconahotel.com/dining', None, 'https://www.mastermechanic.ca/locations/home.php?location=Bolton', None, None, None, 'https://consulmex.sre.gob.mx/phoenix/', None, None, 'http://www.theflowermarketpittsburgh.com/', 'https://truefreedomachievers.com/contact/', None, 'https://functionalwellnesscenteraz.com', '1592277314', None, None, 'http://www.jasonsmithfitness.com', 'http://www.fiorio.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, None, 'http://www.explorersinlearning.com', 'http://www.kre8events.com', None, None, 'https://www.nofrills.ca/store-locator/Tarik%27s+No+Frills+Calgary/3446?storeId=3446', 'http://www.goodcompanycafelv.com', '1592277342', 'https://theeggworks.com', None, None, None, None, 'http://onthespotdrycleaners.com', None, 'http://www.montanamikes.com', 'http://www.bajafresh.com', None, None, None, None, None, 'https://londonfriedchicken.ca', None, None, 'http://the007pub.com', 'http://www.viarail.ca/fr/decouvrez-nos-destinations/gares/quebec/dorval', 'http://www.angelscarpetcarelv.com', None, None, 'https://cortland.com/apartments/anson-at-the-lakes/', 'http://thebarbersshop.ca', None, 'http://www.mastercuts.com', None, 'https://ab.openbox.ca', 'http://www.goodwill.vegas/store-page/coming-soon-retail-storedonation-drive-thru', None, None, 'http://shermanpowerwashing.com', None, 'https://www.greenvalleydentistry.com', None, 'http://www.nextcare.com/locations/az/mesa-power/?utm_sourceYelp&utm_mediumLocal&utm_campaignmesa_power', 'http://www.themarlowapts.com', 'http://www.starbucks.com/store/10311/', 'https://www.issolawfirmlv.com', None, None, None, 'https://barvecue.com', None, None, '1592277404', 'http://www.kirstenlream.com', None, None, None, 'http://www.jamakinmedance.com', 'http://drlegault.ca', 'http://www.feastfoodtours.com', None, None, 'http://www.ulta.com', 'http://surfaceeffectspc.com/', None, None, 'http://www.deltaco.com', None, None, None, 'http://jameswagnerconstruction.com', None, 'http://www.siegelsuitesselect.com', 'http://farmerinthedeli.com/', 'https://www.hertzcarsales.com/phoenix.htm', None, None, None, None, None, '1592277436', 'https://stores.fossil.com/on/vaughan/vaughan-mills-5977/', 'http://www.thalineup.com', 'http://www.ramen-tatsu.com', None, None, None, 'https://www.figuresto.com', 'https://locator.chase.com/az/avondale/1545-n-dysart-rd', 'https://a1dryervents.com', None, '1592277458', None, None, None, 'https://www.usps.com', None, '1592277467', None, 'https://www.ljhaircuts.com', None, None, 'https://transplantcitybeercompany.com', None, 'http://bossproshops.com/Archery/bows.htm', None, 'http://www.mylegalheat.com', None, None, None, None, None, None, None, 'http://www.theredtortilla.com', None, None, None, None, None, 'http://bubbasbonelessribs.com/pages/our-restaurant', None, None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=723&utm_content=bpas', None, 'http://www.klozit.com', 'http://www.nuebrowstobrazilians.com', 'http://www.sichuanhouse.ca/Eng/Default.aspx', 'http://themilkshakefactory.ca', None, 'http://www.audihenderson.com', None, 'http://www.royalpalmshotel.com/spa/scottsdale-spa-menu?src=vanity_alvadora.com', 'https://haircutmenaliantelasvegasnv.com', 'https://www.schorieautorepair.com', None, 'http://www.usps.com', 'https://www.esso.ca', 'http://mimiscarehome.com', None, None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://primeyecare.com', 'https://locations.monro.com/pa/mcmurray/3620-washington-rd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.thewasonline.com', None, None, 'http://www.millersdeliaz.com', 'https://www.tailoredliving.com/southcharlotte/?utm_campaign=LOCAL-YELP&utm_medium=directory&utm_source=yelp', None, None, 'http://www.thebarberschair.ca', 'http://ynotpc.com', None, 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/airdrie-2881-main-street-sw.aspx?storeid=166&code=pc', 'http://www.familymusic.com', None, None, None, 'http://www.metrolinaeye.com', 'http://friendshippet.com', None, None, None, None, 'http://www.shadeusa.com', None, None, 'http://www.saucykytchen.com/', 'http://sites.google.com/site/gamesnatsite/', '1592277585', 'http://www.medigas.com', 'https://www.lakenormandentistry.com', None, 'http://www.spectrumam.com/contact-phoenix.html', 'http://cakesbylori.org', None, 'http://www.thewesthillwinebar.com', None, 'http://www.stansbakery.com/', None, None, None, 'http://suppz.com', 'https://www.bowlmor.com/location/bowlmor-scottsdale?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', None, None, 'http://www.honeysbeestro.com/', None, None, 'http://www.360physicaltherapy.com/locations/physical-therapy-Scottsdale-Thunderbird/', 'http://www.pinkboxpgh.com', 'http://www.mambolounge.ca/', 'http://investorsazrealtors.com', '1592277627', None, None, None, None, 'http://www.altiercu.org', None, None, 'http://www.precision-gymnastics.net', None, 'http://www.fastsigns.com/506', 'http://plumbperfectrepair.com/', 'http://www.mercadodentalaz.com', 'http://fazios-restaurant.com', 'http://www.drhorton.com', 'http://www.amklimo.ca', 'http://www.mcghies.com', 'http://www.tirekingdom.com', None, None, None, 'http://phoenix.org/petsmart-dog-park-at-washington-park/', None, 'http://www.candlesbanquet.com', 'http://www.airfrance.com/cgi-bin/AF/IN/en/common/home/home/HomePageAction.do?WT.srch=1&WT.mc_id=3134951%7C5357760%7C64186796%7C241311732%7C1091631', None, 'http://www.solartopps.com', 'http://www.waynesautomotivemadison.com', None, None, None, None, 'http://romanopanini.com/', 'https://www.bannerhealth.com/locations/sun-city/banner-boswell-rehabilitation-center', None, 'http://www.eccentriclarchmere.com', 'http://www.dollarama.com', '1592277693', 'https://www.chengschinahouse.com', None, None, None, None, None, 'http://www.subway.com', None, None, None, None, None, 'https://www.cyclegear.com', None, 'http://www.sophiesbistro.com', 'https://stores.chicos.com/s/chico-s-shoppes-at-grand-prairie', None, None, None, None, None, 'http://www.bergstrommadisonchevrolet.com', None, 'http://www.goldwingappliancerepair.com', 'http://comparefoodsdirect.com', None, '1592277733', 'http://www.teavana.com', 'http://www.bears-den.ca', 'http://www.thehickorytavern.com/home/hickory_tavern-locations.php?l=Charlotte+-+Providence+Rd.', None, '1592277746', None, None, 'http://shamrockburgers.com', 'http://www.ncguitarworks.com', 'http://www.maritimelobster.ca', None, 'http://www.wingstop.com', 'http://www.thevapeshore.com', None, 'http://www.tcbycanada.com', None, None, None, 'http://www.ocotillofloors.com', None, None, '1592277774', None, 'http://www.chagrinyoga.com', 'https://www.fordmonroeville.com', None, 'https://echo-boutique.com', 'http://www.sswlv.com', None, None, 'http://www.fantasticsams.com', 'http://www.ihg.com/hotelindigo/hotels/us/en/pittsburgh/pithb/hoteldetail', None, 'http://thecountygeneral.ca/cocktail', None, None, None, 'http://www.felicitedayspa.com', None, None, None, None, 'http://stlouiswings.com', None, 'http://cafesociallatinoamericano.com', 'http://www.westechrecyclers.com', 'http://www.urbansmokefoodtruck.com', None, None, 'https://www.safeway.ca/find-a-store/store/8835-safeway-whitehorn', None, 'http://lasvegas.carenow.com/location/arby-durango', None, None, None, 'http://www.brueningglass.com', None, None, 'http://www.modoyogasquareone.com', None, None, 'http://www.bettercoffeecompany.ca/', 'http://crossroads-coffeehouse.com', None, 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, None, 'http://www.barneysboathouse.net', None, None, 'http://www.farinaplus.com', None, 'http://www.mccoolsbarandgrill.com', 'https://mojieatery.com', 'http://www.changjiangdeforest.com', None, 'http://www.figleafboutique.com', None, 'http://www.renewalbyandersen.com/window-company/705-las-vegas-nv.aspx/?utm_medium=localization&engName=social_Yelp&mm_campaign=3553F6E8BDD291901836A46BD410702F&mm_replace=true&utm_source=Yelp', 'https://ioarcade.bar', None, 'https://www.mydrnow.com', None, None, 'https://www1.shoppersdrugmart.ca', 'http://www.kmhlabs.com', None, 'https://www.acapellophotography.com', 'http://www.ouiforeverpet.com', 'http://www.camelrx.com/', None, 'http://www.ultimateelectronics.com/', None, 'http://www.cheesers.com', None, 'http://chase.com', None, 'http://gravityextremezone.com', 'http://www.BetterBathRemodeling.com', 'http://www.chefontheroad.com', 'http://www.cattlebaroncalgary.com', 'http://www.atlantic-vanlines.com', 'http://zen-e-veggie.ca/', 'http://www.paradisebakery.com/store_indiv.php?stid=104', 'http://www.rosehillvenue.com', 'http://sidewalkcafepainesville.com', 'http://www.esenciasalonandspa.ca', None, None, 'http://www.sellingazhomesteam.com', 'http://www.thesiamesecat.com', None, None, 'http://www.svnlounge.com', None, 'http://www.lvplumbers911.com', None, None, 'http://www.urbanthrift.ca', None, None, None, None, 'http://www.cafeneon.ca', None, None, 'http://www.silvereye.org', None, None, 'http://www.toronto.ca/indulge/metrosquare.htm', None, None, 'http://www.starwoodhotels.com/fourpoints/property/overview/index.html?propertyID=1256&EM=YELP_4P_1256_NAD', None, 'http://www.pvtrimmersphoenix.com', 'http://www.phatburrito.com', None, None, None, None, None, None, None, None, None, 'http://www.pizzanova.com/locations/markham.html', None, 'http://www.kryovitalityohio.com/#about', 'http://www.xtsc.ca', None, 'https://giovannispizzeriaandsubs.com', None, 'http://www.shainkertherapy.com', 'http://www.kelseys.ca/', 'http://www.coastcafebar.ca', 'http://www.lonewolfaz.com/', 'http://ahwilkens.com', 'http://communityelectric.ca', None, None, None, 'http://www.monplaisir.ca', None, None, None, 'http://www.senergypower.com', None, '1592277999', 'http://legacyobgynlv.com/', '1592278003', 'http://northvalleyos.com', 'http://4knails.business.site', '1592278010', None, None, 'http://www.lastcall.com/stores/store.jsp?storeId=56', None, 'http://www.gcuhotel.com/', None, None, 'http://thestachecleveland.com', None, 'http://www.newcasaabril.ca/', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.mpbanksdds.com', None, None, None, None, None, None, 'http://luckysilvergaming.com', 'http://www.knappetts.com/', 'http://jyubanramen.com', None, None, None, None, 'http://nvcpc.com/pain-management-clinic-las-vegas-location/pain-management-at-2809-w-charleston-las-vegas-nv-89102/', 'http://alsplumbingllc.com', None, None, None, 'http://www.wekopa.com/', 'https://myhoneybakedstore.com/chandler/2538', None, None, None, None, None, None, None, '1592278070', 'http://oysterbaylv.com', 'http://www.hanger.com', 'http://www.meyersmakeithappen.com', 'http://www.magicutssalons.com/salondetail/default.asp?salonid=5508', None, 'http://www.zerorezcharlotte.com', 'http://rocknoodles.com/', 'http://azeyebrowthreading.weebly.com', 'http://www.purplepenguincafe.com/', 'http://sunrisepediatricslasvegas.com', None, None, 'http://paulsservicecenter.com', 'http://www.arrowheadtownecenter.com/Directory/Details/331672', None, 'http://premierairaz.com/', 'http://www.jackalopelakeside.com/', 'http://www.nailcouturelounge.com', 'http://www.ronijosefsalon.com', None, 'https://www.pittsburghglasscenter.org/', 'http://www.nachodaddy.com/henderson/', None, 'https://www.southwestvanlines.com', 'https://nuage-spa-and-tanning.business.site', None, 'http://www.luckybrandjeans.com', 'http://dvsmiles.com', None, None, 'https://www.naileditsalonscottsdale.com', None, 'http://www.citi.com', 'http://www.esmil.com', None, 'http://www.berthaslasvegaspa.com', 'http://www.salsasmexicanrestaurant.com/', 'https://www.cineplex.com/Theatre/cineplex-odeon-aurora-cinemas', 'https://www.wyndhamhotels.com/hotel/52842?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52842', 'http://www.orthopedicandsports.com/', 'https://www.esso.ca/en/gas-station/etobicoke-on-geesso-200302279', None, 'http://silverarrowsmotorslv.com', 'http://www.warnerstreesurgery.com', 'http://www.bookmans.com', None, 'https://torriopromotionsentertainment.com', None, 'http://www.boarnwing.com', None, None, None, None, None, None, '1592278167', None, '1592278172', None, 'http://intersteer.blogspot.in', None, None, None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZEC', None, None, None, 'https://www.smithsfoodanddrug.com/storeHours?store=70600354', None, None, 'http://www.nikelspot.com', None, 'http://www.pulmonarysolutions.net', '1592278188', None, None, None, None, None, 'http://www.thechickenplace.ca', 'http://www.thehookuptackle.com/', None, None, None, 'https://mylocalmcds.com/willow-pass-concord', 'http://www.hairdynamix.ca', 'http://www.cdglasvegas.com', 'http://www.midas.com/toronto/store.aspx?shopnum=9105&dmanum=857001', 'http://www.desertcarcare.com/chandler-auto-repair-mechanic-shop/', None, 'https://vernlewis.com', 'http://www.bojangles.com', 'https://www.wingstop.com/location/wingstop-979-north-las-vegas-nv-89032/menu', None, 'http://www.yougojumpoc.com', 'http://www.safestreets.com/Yelp', 'https://www.thelittleclinic.com/storeHours?store=85100108', None, 'http://foothillschiro.com/', 'http://www.hanceandhance.com', 'http://naturalchoiceacademy.com/', 'http://www.victoriassecret.com', None, 'https://castdesignteam.com', None, None, None, None, None, 'http://Skinbykarilynn.com', 'http://landing.trugreen.com/yelp?city=Brunswick&state=OH&zip=44212&utm_campaign=ORGANIC&marketingpartner=9817', None, None, None, None, None, 'http://happysushitoronto.ca', None, 'http://www.massagemobilelv.com', None, None, 'http://roundvenue.com/', None, 'http://fitness1gym.com', 'http://www.skinlayers-cosmetics.com', None, 'http://smilingmoonguitars.com', None, 'http://northstandard.com/', 'http://www.photographybytheresarussell.com', None, 'https://www.morgancommunities.com/apartments/pa/pittsburgh/the-docks/', 'http://www.JimmyJohns.com', None, 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', '1592278287', 'http://www.mygcafe.com/', 'http://www.quickspinlaundry.com', None, None, None, 'http://justbrakes.com/Locations/Baseline', None, 'http://www.bobslockandcycle.com/', None, 'https://carolinadigestive.com', 'http://qdoba.com', 'http://www.normansound.com', 'http://azhoneybz.com', 'http://www.anylabtestnow.com/Glendale', 'http://www.bathandbodyworks.com', None, 'http://www.azneurosurgery.com', 'http://www.beyondbeautyskincare.com/', 'http://www.nexthorizons.org', 'http://www.avalon-scottsdale.com', None, None, None, 'http://www.creteus.ca', None, None, 'http://www.keymanlawncare.com', None, 'http://www.doctordetailofmatthews.com/', 'http://www.Childrenslung.com', 'https://bostonpizza.com/en/locations/sunridge.html', 'http://www.foodbaraz.com', 'http://www.kumon.com/HENDERSON-GREEN-VALLEY-NORTH', 'https://locations.theupsstore.com/oh/brecksville/8803-brecksville-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://www.rogers.com/small-business/contact-us/store-locator?store=17111', None, 'https://clubhousecf.com', None, 'http://gentledoctor.com', 'http://www.hallspestcontrol.com', None, None, 'http://www.dawat.ca', 'http://summitcc.org', None, 'http://www.rokaakor.com/locations/scottsdale', 'http://www.caricaturecinema.com', 'http://www.adamsdriveshaft.com', None, None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.yogathletix.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://www.anytimefitness.com', None, 'http://moondoggieslasvegas.gooddinner.space', 'http://www.kimflorist.com', None, 'http://www.teriyakiexperience.com/', '1592278399', 'http://www.tastybunz.com/', 'http://oliveandmarlowe.com', None, 'http://www.germanautotec.com', None, '1592278409', None, None, 'http://www.360physicaltherapy.com/locations/physical-therapy-Phoenix/', None, 'https://www.mercadodaweb.com/local/detalhes/sculpture-nail-and-spa', None, None, 'http://www.goldeneggrollaz.com', None, 'http://www.torontodancesalsa.ca/', None, 'https://my.clevelandclinic.org/locations/directions/423-akron-general-health-and-wellness-center-bath', None, 'http://www.pikenursery.com', 'https://silvertoncasino.com/dining/shady-grove-bar-and-lounge/', None, 'http://www.pizzapatron.com', None, None, 'http://pawsitivelynatural.com/', None, None, None, 'http://www.thebirthdaysuit.com', 'http://www.altenburgstudio.com', None, None, 'https://locations.cariboucoffee.com/us/nc/charlotte/4327-park-road', '1592278457', None, 'http://www.shell.us/', None, None, None, 'https://locator.chase.com/az/anthem/39516-n-daisy-mountain-dr', 'http://www.stouffvillevetclinic.com', 'https://www.aucoq.ca/fr/nos-restaurants/3-verdun.html', 'http://www.ceramictilephoenix.com', None, None, None, 'http://foodtruckfridaycharlotte.com', 'http://www.sportcycle.ca/', 'http://www.patsdrycleanersaz.com', None, None, None, 'http://www.twistedcultures.com', None, 'http://yorkusmiles.ca', None, None, None, 'http://www.open-sesame.ca', None, None, 'http://nevadacardiology.com', None, 'http://cellardoorvintage.com', 'http://www.moda-nc.com', None, 'http://www.myopracticsaz.com/', None, None, None, None, 'http://cali-nails-spa.business.site', None, 'http://www.drgoldman.com', None, 'http://www.levinfurniture.com', 'http://www.riverviewparkapartments.com', None, None, None, None, 'http://www.plazaappliancemart.com', None, 'http://www.springchinahouse.ca', 'http://greatharveststow.com', 'http://www.harpersgroup.com/harpers.asp', 'http://www.big5sportinggoods.com', None, 'http://www.boldroost.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', None, None, None, 'http://www.dickeys.com/', 'http://www.azheartrhythmcenter.com', 'http://activelifepaincenter.com', 'http://ww3.truevalue.com/vogt/MapLocation.aspx', 'http://www.bp.com', None, 'http://www.seatcoversunlimited.com', 'http://www.modernlv.com', None, None, None, 'http://qdoba.com', None, 'http://www.ranchoministorage.com', None, 'https://www.thehatco.com/', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://www.ulta.com/stores/charlotte-nc-590', 'http://www.builtbygrace.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://snipits.com/locations/gilbert', None, 'http://www.thedunfield.com', 'https://www.choicehotels.com/nevada/las-vegas/rodeway-inn-hotels/nv050?source=pmfyelp&pmf=yelp', None, None, None, None, 'http://www.paradisebakery.com/store_indiv.php?stid=10', 'https://www.expressoil.com/stores/fort-mill/sc/6100/', None, None, None, None, 'http://pizzagigi.ca', None, 'http://www.eaturbanpicnic.com/', 'http://www.buccis.net', None, None, 'http://www.nativehealthphoenix.org', 'https://www.stationatpoplartent.com', 'http://www.bbb.org/pittsburgh', None, None, 'http://www.dryclean-usa.com', None, None, 'http://phoenixeyebrows.com', None, None, None, 'http://signup.orkin.com/orkin/res/fun-standard-pph_pcb_tph_tsch.aspx?utm_source=yelp&utm_medium=internet-yellow-pages&utm_campaign=YELP1312', '1592278640', 'http://www.stoolpigeons.biz', None, 'http://613grill.com', None, None, None, None, None, 'http://www.usps.com', 'http://www.futureshop.ca/', None, None, None, 'http://www.ihg.com/holidayinn/hotels/us/en/toronto/yyzty/hoteldetail', None, None, None, 'http://www.golfclubinc.com', 'http://offthegridfitness.com', 'http://www.yumtum.ca', 'http://iwasframed.biz', None, None, None, 'http://bentalasalon.com', 'https://solexotica.com/169-church-st-toronto.php', 'http://driscollsandsonscafe.com', 'http://www.lasvegasdestinationweddings.com', None, None, 'http://www.podeli.com/', None, 'http://www.cutecutsformutts.com', None, 'https://shopcuttings.com', '1592278699', 'http://www.familypm.com', None, 'http://www.appledentistry.net', 'http://destinationacademy.com/', 'http://www.coach.com', 'https://www.premierobgynlv.com', 'http://www.elyriachinabay.com', 'http://www.brewandgrow.com', '1592278718', None, None, 'http://www.emergencychiropractic.com', None, None, 'http://www.pandb.ca/', 'https://www.westelm.com/stores/ca/on/toronto-shops-at-king-liberty/', None, None, 'http://www.salon27az.com', None, 'http://www.kassmanorthopedics.com', None, None, None, 'http://goldencrownamherst.com', None, None, None, 'https://www.cricketwireless.com', None, 'https://thericebox.com/catering', '1592278743', 'http://www.jackinthebox.com/', 'http://www.associaarizona.com', None, '1592278750', 'http://www.lelyonnaispgh.com', None, None, 'http://www.serendipitycinema.com', None, None, 'http://jpbargrillto.wordpress.com', None, None, None, None, 'http://www.swirlingwindvapors.com', 'http://www.sundevilauto.com/locations/az/gilbert/gilbert-21', 'http://www.gasolinealleyinbath.com', 'http://nestlecafe.com', '1592278774', 'http://www.moreheadsttavern.com/', None, 'http://www.scottsdaletradingpost.com', None, None, 'http://www.cellzrepair.com', 'http://www.drbonniewan.com', None, 'http://www.soupersalad.com', None, 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'http://meatandeggsales.illinois.edu/', 'http://www.kellyspa.com', None, None, None, 'http://www.montessorictr.org', 'http://www.ossingtonchiro.ca', 'http://bigfatburrito.ca', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.studio30ink.com', None, 'http://www.artfulcakes.ca', None, 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', None, 'http://DrApigo.com', None, None, None, None, 'http://www.greenplanetlandscaping.com', None, 'http://www.windsorarmshotel.com', 'https://qualitycharlottegranitecountertops.com', 'http://www.lileinsteinspreschool.com', None, None, 'http://www.figarosalon.com', None, None, None, 'http://www.snackmrkt.ca', 'http://www.kristenkruger.com?cmpid=PRHC_BLM_0006', 'http://www.urgentcareofaz.com', None, 'https://www.sunsetgrill.ca', 'http://www.bdhginc.com/bigDogsCafeCasino/', None, 'http://www.cevascojewelers.com', None, 'http://www.pennbrew.com/', 'http://www.thermoshieldinsulation.com', 'http://www.rotorooter.com/cleveland/?cmpid=21972', 'https://enjoynailsandspa.business.site', 'http://www.jjqs.ca', None, 'http://meltgrilledcheese.com', '1592278866', 'http://www.officialroyalnailsandspalv.com', 'http://dukepubs.ca/devon/', 'http://www.tacobell.ca', None, 'http://www.teksystems.com', 'http://unitedconcessionsgroup.com/brandspartners/bar-symon/', None, None, 'http://www.loxandschmear.com', None, None, None, 'https://www.barbecueworld.com/barbecue-world---vaughan', 'http://www.greenlocksmithaz.com', None, 'http://www.fantasyfarm.ca/', None, 'http://www.defconpaintball.com', 'http://www.manorsuites.com', 'http://www.uppercrustoh.com', 'https://www.onezotapioca.com', None, None, 'http://www.mobile-depot.ca', None, None, 'http://www.sacredfeather.com', None, None, 'http://www.boconcept.com/en-ca/stores/find-your-local-store/canada/boconcept-calgary', 'http://solterrasl.com/subacute', 'http://www.360customsllc.com', 'http://www.4wheelers.com', None, '1592278926', '1592278928', 'http://www.offthecuffdowntown.com', None, 'https://www.sunrisepreschools.com/locations/baseline-gilbert/?utm_source=yelp&utm_campaign=online_listing_gilbert_280&utm_medium=referral&utm_term=business_url', None, None, 'http://www.solidautorepair.com', None, 'https://www.yrts.ca', 'http://www.littledreamerproductions.com', 'http://myhomevegas.com', None, 'http://www.lifelabs.com/Lifelabs_ON/locations/location_details.aspx?LocationId=239', None, 'http://www.awtravelaz.com', None, 'http://www.arialasvegas.com/dining/restaurants/roasted-bean', None, 'http://www.lavecchias.com', 'http://www.simplyhousekeepingaz.com/', 'http://www.arbys.com', None, None, None, 'http://www.menchies.com', 'http://moovingbuddies.com', 'http://www.vcahospitals.com/fox-chapel/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Fox_Chapel_Animal_Hospital&utm_campaign=main_url', None, 'http://www.caesarspalace.com/casinos/caesars-palace/casino-entertainment/shania-twain-detail.html', None, 'https://www.greatdanepub.com/location/downtown', 'https://www.paintingwithatwist.com/akron-fairlawn', None, None, None, None, None, 'https://www.carwashstrongsvilleoh.com', 'http://www.dominos.com', 'https://stores.petco.com/az/scottsdale/pet-supplies-scottsdale-az-1109.html', 'https://www.deltahotels.com/Hotels/Delta-Calgary-Airport-Hotel/Restaurants-Dining/Compass-Restaurant', 'http://www.storage24x7.com/index.php?option=com_rent_a_unit&view=detail&id=2&Itemid=179', 'http://www.monexgroup.com', 'http://www.JimmyJohns.com', 'https://williamsfreshcafe.com/location-source/brampton-central-park-dr/', 'http://www.sunshinehealth.net/', 'http://www.sushitei.ca', None, None, None, 'https://www.goldencorral.com/locations/679/golden-corral-n-anderson-road', 'http://royallinksgolfclub.com', 'http://maidsonthespot.net', None, None, None, None, None, None, None, 'http://www.superiortire.ca', 'http://www.leswan.ca', 'http://www.eyelashjunkieonline.com', None, None, None, 'http://theinvigory.com', 'http://www.fullcycleinsurance.com', None, None, 'http://www.tamalehutlv.com', '1592279054', None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, None, None, None, 'http://www.abchomespecialists.com', 'http://www.verizonwireless.com/stores/north-carolina/gastonia/gastonia-319517/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, None, None, 'https://www.sohohouse.com/houses/soho-house-toronto', 'http://charlotte.junk-king.com', 'http://www.ladymosquito.ca', 'https://cyclebar.com/location/north-hills', None, 'http://www.prohealthsp.com', None, '1592279085', None, None, 'http://estrellataqueria.ca/', 'http://www.powerrancharborists.com/', None, None, 'http://www.brightnow.com/locations/dental-office/Phoenix/Bright+Now+Dental/40020', 'http://www.pizzanova.com', None, 'http://www.agakhanmuseum.org', 'http://www.treeservice-mesa.com', 'https://www.canadaswonderland.com/play/haunt', 'http://www.caesarspalace.com', 'http://stumpplants.com/cleveland', 'http://geaugavision.com/lakewood/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.ushaircutters.com', 'http://local.biglots.com/oh/north-olmsted/5206', None, 'http://www.cozydrycleaners.com', None, 'http://www.vinorosso.ca', None, None, 'https://locations.theupsstore.com/wa/kent/325-s-washington-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://themunchiescafe.net', 'https://nelsonestatejewelers.com', 'http://www.bbblack.com', 'http://www.spencersonline.com', None, None, None, 'http://MarketDistrict.com', None, None, None, None, None, None, 'http://www.restorativemassageskincare.com', None, 'http://www.phoenixlettering.com', 'http://www.spadewestmount.com', None, None, None, None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, None, '1592279173', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.hirethegardener.com', None, None, 'http://www.choprayoga.com', 'http://www.7-eleven.com/?yelp=29384', 'http://boulderplacement.com/', None, 'http://www.winestylessunprairie.com', None, None, None, 'http://www.acorngas.com/', 'http://www.constantinesgardencenter.com', 'http://www.deltacarpetslv.com', None, None, None, None, None, 'http://retail.theartofshaving.com/retail/locations/fashion-square', 'http://www.biketheburgh.com', 'http://www.torontopearson.com/', 'http://midtownhwc.ca', None, 'http://www.alianteapts.com/', 'http://www.shieldsfamilydentistry.com', None, 'http://www.mobilepetgroominglv.com', None, None, 'http://www.v3pizza.com', None, 'https://www.ginospizza.ca', None, 'http://www.marcos.com/locations/oh/lorain/leavitt-rd?s=true', 'https://theresortatsummerlin.com/dining/casual-dining/promenade-cafe/', None, None, None, None, 'http://www.pizzafactory.com/las-vegas', 'https://www.ohiobasementsystems.com/?utm_source=yelp&utm_medium=display&utm_campaign=obs-twinsburg', 'https://elsupermarkets.com/las-vegas-1255-s-lamb-blvd-nv-89104/', None, 'http://bevelhair.ca', 'https://www.mainevent.com/location/pennsylvania/pittsburgh/15275?utm_campaign=localmaps&utm_medium=organic&utm_source=yelp', '1592279256', None, None, 'https://www.300automotive.com', None, 'http://www.aliantecasinohotel.com/dining/camachos.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=AS&utm_content=AS-PROPERTIES&utm_campaign=AS-YELP', None, '1592279265', 'https://plumbingbliss.com', None, None, None, None, None, None, None, 'http://www.sailfin.com/', None, 'https://www.yellowtailusa.com', 'https://mrosmow.com/shawarma-aurora-wellington/', None, None, None, None, 'http://www.rt91harvest.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, None, None, None, 'http://www.arboretumobgyn.com', 'http://www.ravellotownhomes.com', None, None, None, '1592279310', None, None, 'http://a1garage.com/tempe', 'http://www.kingscollegecharlotte.edu', 'http://www.michaelsonchurchview.com/', 'http://www.ipsaarizona.com', '1592279323', 'https://clicknathan.com', 'http://7thstreetpublicmarket.com/', 'https://experimax.com/locations/henderson-nv/?client=8014-80013&campid=20&utm_source=yelp&utm_medium=CPC&utm_campaign=yelp_ad', None, 'https://www.phoenixatvjetskirental.com', None, 'http://www.arbys.com', 'https://www.gigisonfairmount.com', 'http://www.burgerbob.ca', None, 'http://www.aeolianstrings.com', 'http://www.papajohns.com', 'http://nevadamademarijuana.com', None, None, None, 'http://www.drivegolan.com', 'http://www.circledesalon.com/', None, None, None, None, None, 'http://www.be-electronics.com', None, 'https://drcosta.com', None, None, None, None, None, 'http://Www.saborcharlotte.com', None, 'http://www.lilacfestival.net/', None, None, None, None, 'https://rusticpathways.com', 'https://www.albopizza.net', 'http://www.greenleafvolare.com', 'http://www.53.com', 'http://www.mod-meals.com', 'http://www.empireyards.ca/', 'http://buroakdental.com', None, 'http://www.atamisushi.com/', 'https://pittsburgheyeassociates.com', 'http://www.eduardosreceptionhall.com', None, None, None, None, 'http://www.eurolite.com', 'http://www.dunkindonuts.com', 'http://preschool.sgcslv.com', None, 'http://www.govig.com', 'http://www.brookeorthodontics.com', 'http://bellwoodsbrewery.com/', 'https://www.sasfabrics.com', None, None, None, None, 'http://www.beddingtontownecentre.com/?page_id=85', None, 'http://www.steaknshake.com/locations/24203-steak-n-shake-home-avenue-akron', 'http://www.topazvet.com', '1592279435', None, 'http://allaboutbeer.com/gather-for-beer/nc-brewers-celebration/', None, '1592279439', None, 'http://www.kmart.com/stores/kentucky/henderson/3688.html', None, 'http://www.pmgaz.com', 'http://crankymonkeybikeshop.com', None, None, 'http://www.mktbistro.com', None, None, None, None, None, '1592279459', 'http://www.matthewsfamilychiropractic.com', 'https://www.hertz.com/rentacar/location/canada/alberta/calgary/YYCO12', 'https://www.homedepot.com/l/Peoria/AZ/Peoria/85345/453?cm_mmc=seo-yelp&', None, 'http://www.lvyao.org', 'http://golfwing.ca', None, 'http://avocadosushi.food94.com', None, None, 'http://salesandservice.cummins.com', None, None, None, 'https://www.petsmart.com/stores/us/pa/tarentum-store1525.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', None, None, None, 'http://shishaliciouscafe.ca/', None, 'http://105cigarco.com/', None, 'https://www.bonefishgrill.com/locations/nc/charlotte', 'http://www.betterchoicehomes.com', 'https://www.petsmart.ca/stores/ca/ab/calgary-store1201.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', None, None, 'https://trufusion.com/schedule-summerlin/', 'http://www.cashamerica.com/CASHAMERICAPAWN-stores/NC/CHARLOTTE/Cha05', None, 'https://www.supercuts.com/locations/az/glendale/bell-park-shopping-center-haircuts-80215.html', 'http://brunsell.com', 'http://antiqueplazamesa.com/', 'https://www.marriott.com/hotels/travel/lastw-towneplace-suites-las-vegas-city-center/', None, None, None, None, 'http://www.BallantyneReading.com', 'http://www.ladderupmarketing.com', 'http://www.pruitts.com', 'http://www.lunchdate.com', 'http://www.ritzcarlton.com/charlotte', 'http://www.marriott.com/hotels/travel/phxcd-residence-inn-phoenix-chandler-fashion-center/', 'http://mesapropertymanagement.com', None, None, None, None, None, None, 'https://coppersprings.com', None, 'http://ispoonful.com', None, None, None, 'http://www.madraspalace.com', None, None, 'http://www.43aah.com', 'http://Sincityflying.com', None, None, None, None, 'http://www.hottopic.com', 'https://local.albertsons.com/az/scottsdale/6965-n-hayden-rd.html', None, None, None, None, 'http://www.amadeuselectric.com', None, 'http://www.JimmyJohns.com', 'http://www.suncitydentalcenter.com', 'http://www.childtime.com/your-local-school/phoenix-az-1408/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'https://www.elephantcastle.com', None, 'http://www.drivemorriscadillac.com', 'http://www.abercrombie.com', None, None, None, None, None, 'http://www.sstireaz.com', 'http://habibi-barber-shop.business.site', None, 'https://www.thecoreinstitute.com', None, 'http://www.charlotteballet.org', None, None, 'http://www.royaldanceworks.com', 'http://www.panaceaecoshop.com', None, '1592279612', 'http://www.wireonewisconsin.com', None, None, None, 'https://www.inthegroove.com', None, None, 'http://www.asui.org/contact-us.php', None, '1592279625', 'http://www.theundergrounddance.com', 'http://www.undergroundshirts.com', 'http://www.stoneridgesquare.com', 'https://www.uniteddebtreduction.com', 'https://www.winners.ca', None, None, 'http://www.autorepairsmesa.com', None, 'http://www.primrosefortmill.com?utm_source=yelp&utm_medium=maplistings&utm_campaign=localmaps', 'http://www.goldenglow.ca/', 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1317', None, None, None, None, 'http://www.downtowntempe.com/6thstreetmarket', 'http://www.slamnv.org', '1592279660', None, 'http://www.pizzamaster.online', 'https://www.cosmickidsdental.com/?utm_medium=lpdg-yelp&utm_campaign=Yelp%20Desktop&utm_source=Yelp', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.vanityvapor2.com', 'http://www.sallybeauty.com', 'http://www.thepubchipshop.com/food-truck/', 'http://www.azulpoolandspaservices.com', 'https://lostaquitosaz.com', None, 'https://www.omnihotels.com/hotels/montreal-mont-royal?utm_source=yelp&utm_medium=sponsored&utm_content=MONDTN&utm_campaign=sponsored-website', None, 'http://www.charlotterusse.com', 'http://avasalley.webs.com', None, 'https://www.storquest.com/self-storage/az/chandler/9039', None, 'http://www.advancedbiosolution.com', None, None, 'http://www.cyclopautomotive.com', None, 'http://www.pizzapizza.ca', 'http://www.tsaesthetika.com', 'http://www.starlettnailsandspa.com', 'http://www.pizzanova.com', 'http://www.skintopiaaz.com', '1592279714', None, 'http://fairlawn.dentalworks.com', None, 'http://www.JimmyJohns.com', None, None, 'https://onehourcafeteria.wordpress.com', None, 'http://www.ckgrill.com', None, None, None, 'http://www.polkadotsplayland.com', 'http://donvincenzoristorante.com/', 'http://www.bakkechiropractic.com/Sun-Prairie.html', 'http://website-255841605104462012194-restaurant.business.site', None, None, 'http://concordfoodcentre.com', None, None, None, None, 'http://www.swrxlv.com', None, None, None, '1592279756', 'https://bostonpizza.com/en', None, 'https://www.perfectingthesmile.com', 'http://serenitynailsspalv.com/', 'http://www.yogurtology.com', 'https://website-8304873588433377338-bubbleteastore.business.site', None, 'http://www.mowandcliplawncare.com', None, 'http://www.sportinglife.ca/', 'https://satruck.org', 'http://www.eezfusion.com', None, 'http://www.HealthPlanofNevada.com', None, None, None, None, 'http://www.secondcup.com/location/montreal-3365-s-boul-des-sources-ddo', 'http://www.phoenixcoffee.com', None, None, 'http://www.shieldfs.com', 'https://www.speedway.com/StoreDetails?store=2906', None, 'http://www.competitivepoolservice.com', 'http://www.donnakohlhase.net?cmpid=JO8H_BLM_0006', 'https://www.weinercompanies.com', None, None, 'http://www.kopsrecords.ca', 'https://www.santarosaapartmenthomes.com', None, None, 'https://www.sprint.com/storefronts/bd/sprint-gastonia-nc-28054-fcs-2094/?ecid=SEO:Yelp:2020_Q1:LastMile', None, 'http://www.potbelly.com/Euclid?utm_source=ExtNet&utm_medium=organic&utm_campaign=Yext', '1592279828', 'http://www.thecommonslv.com?campaign_code=yelp_The_Commons_NV_89014', None, '1592279834', 'https://www.bostonmarket.com/location/lyndhurst-oh-139/', 'http://www.goodwill.vegas/store-page/attended-donation-center-stephanie-horizon-ridge', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://locations.theupsstore.com/az/tempe/1753-e-broadway?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.tangerineasiancuisine.com', None, 'http://www.oxfordathleticclub.com', 'https://www.hilton.com/en/hotels/phxtpes-embassy-suites-phoenix-tempe/?SEO_id=YELP-ES-PHXTPES', None, 'http://www.wellnessinstituteofnv.com', 'http://www.loblaws.ca/', 'http://thestagestar.com', 'http://www.attrellhyundai.com/', 'http://www.bluefallscarwash.com', None, 'http://www.stillwaterapts.com', None, None, 'https://www.mcfalltire.com?utm_source=yelpURL', None, None, 'https://www.goodsplumbing.com', None, None, None, 'https://www.ncsecu.org', 'http://www.ultimatestaffing.com', None, 'http://dekra.us/en/nevada/las-vegas-6020-n-decatur-blvd/', None, None, 'http://www.TrainWalkPoop.com', None, None, 'https://www.chick-fil-a.com/wexford', '1592279883', None, 'https://newmanurology.com', 'http://www.aperfectpatio.com', 'http://www.ligardeneastlake.com/', 'https://www.plannedparenthood.org/health-center/nevada/las-vegas/89102/las-vegas-west-charleston-2304-90210?utm_campaign=las-vegas-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', 'https://www.enterprise.com/en/car-rental/locations/us/co/avon-vail-1224.html?mcid=iyp:8368400', 'http://stoughtoncountryclub.com/', 'http://www.gilbertair.com', None, None, 'http://www.jerryscampingcenter.com', None, 'https://www.holisticmidwifenv.com', 'https://insomniacookies.com/locations/store/1139', None, None, None, 'https://bmcmattress.com?utm_source=Yelp&utm_medium=organic&utm_campaign=PhoenixJanMar2018&utm_content=website-organic', '1592279918', None, None, None, None, 'http://www.holycrepefoodtruck.com/', None, 'http://www.abelfloors.com/', 'http://www.heartbreakerguitars.com', None, None, None, 'http://telsaan.com', None, None, 'http://www.northernhillschiro.ca', None, None, None, 'http://www.bullandbarrister.com', 'http://lvkarate.com', 'http://www.ncmovinglabor.net/', None, None, 'http://www.hardrockhotel.com/entertainment/vinyl', 'http://www.dentistoakville.com', '1592279960', None, 'http://www.jfjtoronto.com', 'http://transitionaldesign.net/resale-shop/', None, 'http://marketavenuewinebar.publishpath.com', 'http://www.brazastone.com', 'http://www.frysfood.com', 'http://athenapizza.ca/fr/', 'http://www.murale.ca', 'http://www.speedysac1.com', None, 'https://www.montecarlo.com', None, 'https://walkerfurniture.com/en/furniture-stores-henderson-marks-st', None, 'http://athenagreekcuisine.com', None, None, None, None, None, None, None, 'http://drgregceyhan.com', None, None, 'http://www.bellablueboutiquemesa.com/', None, None, 'http://kababhousephx.com/', 'http://www.PhoenixNaturalDoctor.com', 'https://www.lasvegasdodge.com', None, None, None, 'https://stores.bestbuy.com/pa/pittsburgh/430-home-dr-584.html/?loc=ns100&ref=NS', 'http://pittsburghicearena.com/', None, None, None, 'http://www.tamarakapartments.com', 'http://chutneyrolls.com/', 'https://twomenandatruck.com/movers/nc/charlotte', 'http://www.fat-tuesday.com', 'http://azfreehomelistings.com/', None, None, 'http://www.pizzapizza.ca', None, None, 'http://www.qualitytowing.com', 'https://familytrust4you.com', 'http://www.greenthaifusion.com', 'http://www.thecoffeebuddha.com', 'http://www.ecoguardpest.com', None, None, 'http://www.maxandermas.com', None, 'https://www.tequilafamilymexicanrestaurant.com', None, 'http://Thelashstudio.ca', 'http://www.vitaminchamp.com', 'http://www.orbitrestaurant.ca/', None, None, 'http://www.americanleakdetection.com/las-vegas/', None, 'http://www.massageheights.com/locations/pa/pittsburgh-pa/bakery-square', None, 'https://www.cubesmart.com/north-carolina-self-storage/huntersville-self-storage/3406.html?utm_source=yelp&utm_medium=link&utm_content=facilitylistings&utm_campaign=brand&phid=3406', 'http://www.pancheros.com', None, 'http://www.wist.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006430627140&ds_s_kwgid=58700000443429122&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'https://www.pearsoneyecare.com', 'https://salon1226.com', None, 'http://www.povertyspets.org/', 'http://www.cornerbakerycafe.com', 'http://www.bentleyscoffee.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006432138232&ds_s_kwgid=58700000444979854&ds_url_v=2', 'http://qbds.net/speakeasy/', 'https://www.mogaspizza.ca', None, 'https://irepair.ca/pages/mississauga', 'http://www.redmtndental.com/', 'http://www.babbittmotorwerks.com', 'http://ziebart.com/find-my-local-ziebart/location/madison-wi', 'http://www.BattlefieldVegas.com', 'http://northscottsdalechildrensdentist.com', None, 'http://www.arizonataste.com', 'http://www.costco.com/warehouse-locations/thomas-road-phoenix-az-465.html', 'http://www.tropicalsmoothiecafe.com', None, None, None, None, 'https://www.primeyecare.com/mesa.html', 'http://www.jetsetsmiles.com/', 'http://www.talkingstickgolfclub.com', None, 'http://www.ambiancehairsalon.com', None, None, 'http://kingswayjunctionchiropractic.com', None, None, 'http://www.oohlalabeautybar.com', None, None, 'http://www.sugarmarmalade.com', None, None, None, None, 'http://www.bbcello.com', None, 'http://www.mrlube.com/en/mr-lube-near-you/Locate-a-Mr-Lube/concord-8555-keele-street.aspx?storeid=45&postalcode=L4K%202N1', 'https://stores.toysrus.com/az/mesa/toy-store-mesa-az-5651.html', 'https://www.bannerhealth.com/locations/sun-city/banner-lakes-imaging-center', None, None, 'https://locations.wendys.com/united-states/oh/south-euclid/4037-mayfield-road', 'http://www.originalpancakehouse.com', 'http://www.lewiswealthadvisors.com', 'http://hermanspubandgrub.com/', None, None, 'http://www.bellissimo.ca', None, 'http://kidzpreschool.com/contact/mountainsedgeandsouthernhighlands', None, 'http://www.miragelimo.com/', 'http://rushlaneto.com', None, 'http://atwoodeuropean.com', None, None, None, 'https://www.aritzia.com/en/store?StoreID=aritzia-bloor-flagship-toronto', 'http://www.evfas.net', 'https://jadenailandspa.com', None, None, 'http://www.scdsaz.com', 'https://www.alidaspgh.com', 'http://www.vossag.com', 'http://www.dollarama.com/', None, None, 'http://www.vioc.com', 'http://www.sullysmedina.com', 'http://surestop.ca', None, 'http://www.hairwave.ca/', 'http://www.krepesz.com/', None, 'http://www.sugarandspiceeatery.com/', 'http://local.firestonecompleteautocare.com/arizona/peoria/10661-n-84th-ave/?lw_cmp=IYP_YPC_MLP_11932', None, None, 'http://www.grooveejuice.com', None, 'http://www.aeropostale.com', None, 'http://universalsolutionswindows.com', None, None, 'http://MegaFitAz.com', 'https://www.youfit.com/gym/mesa-recker-rd-5468?utm_source=local&utm_medium=yelp&utm_campaign=club5468&utm_term=website', '1592280256', None, None, None, 'http://www.shop.ca/', None, 'https://www.azimportgarage.com', 'http://www.los-arcos-restaurant.com', 'http://www.mtspainting.com', None, None, 'http://paradisebouncers.com', 'http://pbmassageaz.com', None, None, None, 'http://www.videobabylon.ca', None, 'https://azautotime.com', 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', 'http://www.tenfoothenry.com', 'http://www.esthershomemadecandy.com', None, None, 'http://www.walkintubs-install.com', 'https://pizzadrafthouse.com', None, 'https://www.homedepot.com/l/Henderson/NV/Henderson/89014/3302?cm_mmc=seo-yelp&', 'http://www.reliabledrain.com', '1592280311', 'http://www.budgettruck.com', 'http://www.nolasvegasbugs.com', None, None, 'http://www.deanhonda.com', None, 'http://www.sagerealestate.ca', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___north_gilbert_superstition', None, None, 'http://www.upmc.com/Services/dermatology/department-of-derm/Pages/default.aspx', None, 'http://extremereloadingnv.com/', 'http://www.PuffVaporStore.com', None, 'http://themilliken.ca', None, 'http://www.myhealingwaterslv.com', 'http://www.healthquestpa.com', None, None, None, None, None, 'https://www.tgifridays.com/locations/1817/fridays-bethel-park-pennsylvania', 'https://jamiescottfitness.com', None, 'http://www.piesunlimited.com', 'http://www.canarysfamilyrestaurants.com', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.stmarysmadison.com', None, 'http://www.westislandcats.com', 'http://www.dormontvision.com', None, None, None, 'https://www.smithsfoodanddrug.com/stores/details/706/00334', 'http://www.edisonspub.com/', None, 'http://www.fairwaychevy.com', None, 'https://www.goldencorral.com/locations/965/golden-corral-brookpark-road', 'https://locations.wendys.com/united-states/az/gilbert/929-n.-arizona-avenue', 'http://thunder-cloud-optical.business.site', None, '1592280396', None, 'http://www.stjohnsaz.org', 'http://www.fortunescoffee.com/', 'https://local.fedex.com/az/tempe/office-4524/?cmp=LOC-1001545-3-1-971-1110000-US-US-EN-YEXTLISTFXOSHIP', None, None, '1592280409', None, None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.htspittsburgh.com', None, None, 'http://corralwestadventures.com', 'http://www.pennmurry.com', None, 'http://phoenix.tuxedomoving.com', '1592280429', 'http://www.briggscollision.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://lapochkintax.com/', None, 'https://www.cardinalhvac.com', None, 'http://salonmetaxa.com', 'http://www.salonkrush.com', 'http://www.desertlocksmithaz.com', None, None, 'http://www.bobgillinghamford.com', 'http://www.nchairstudio.net', None, None, None, None, None, 'http://www.ocotilloanimalclinic.com/', None, None, None, 'https://www.roberthalf.com/locations/az-phoenix/10835-n-25th-avenue', None, 'https://www.cohenfamilylaw.com', 'http://www.terrawest.com', 'http://www.honeycuts4men.com', 'http://www.monclergroup.com/wp-content/uploads/2014/09/2014-settembre-moncler-toronto-eng.pdf', 'http://grabbagreen.com/places/united-states/arizona/scottsdale/open-location/phoenix-4727-e-bell', 'http://www.crossfitlasvegas.com', 'http://adultworldlasvegas.com', 'http://www.anaboutique.net', None, None, 'http://www.queencityhealthcenter.com/', None, None, 'http://www.waterbeauties.com', 'http://hiltongardeninn3.hilton.com/en/hotels/ontario/hilton-garden-inn-toronto-airport-YYZTAGI/index.html?SEO_id=YELP-GI-YYZTAGI', None, None, '1592280492', 'https://yearinlaw.com', 'http://www.1133westfifthapts.com?campaign_code=yelp_1133_West_Fifth_AZ_85281', 'https://www.e7health.com', 'http://wingwarehouse.com/', None, 'http://www.registryvacations.com', 'http://www.sallybeauty.com', None, 'http://www.fourseasonsnatural.com/main/page_home.html', 'http://innercitymma.com', None, None, None, None, 'http://www.funkyjunkrestore.blogspot.com/p/about-us.html', None, None, '1592280521', None, 'http://www.madisonclinic.net', 'https://www.chocolatsfavoris.com', None, None, 'http://www.gfs.com', 'http://www.phillipscliniclv.com/', 'http://cuyahogalibrary.org/', None, 'http://jetdevelopmentinc.com', 'https://www.thinkpro.net', 'http://www.ontargetcarpetcleaning.com', None, None, 'https://www.budget.com', None, None, 'http://www.all-safesecurity.com/about.aspx', 'http://azpaindoctors.com', None, 'http://www.glomedspas.com', '1592280555', None, None, None, None, None, None, 'https://www.vivida.com', None, None, 'http://playdaycafe.com', 'http://www.beasbraiding.com', None, 'http://www.bishoplawoffice.com', None, None, 'http://www.smithchiro.net', 'http://www.nationwidegaragedoorproducts.com/repair-service-las-vegas-award-authorized-dealer.html', 'http://www.marriott.com/phxgb', 'http://www.bananarepublic.com', 'http://www.bar-4u.com/', None, None, 'http://l.macys.com/biltmore-fashion-park-in-phoenix-az?cm_mmc=Yelp_Stores-_-Phoenix-_-n-_-451&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Phoenix_451&m_ac=yelp_stores&m_ag=n', 'http://www.racelab.com', None, 'http://www.totalvegasrealestate.com', None, 'http://www.babettebeautee.com', None, None, 'https://www.ediblearrangements.ca/stores/250-7th-Ave-SW-Calgary-AB-T2P-0W6', 'http://www.orleanscasino.com/relax/spa?disid=wmm_yelp_to_corporate_spaorleans_organiclink', None, None, 'http://www.portraitinnovations.com/', None, None, 'http://www.floret.ca', 'https://www.restore1.net', None, None, None, 'http://gadaboutvintage.com', 'http://aztagstitleregistration.com', None, None, 'http://www.dqvet.com', None, 'https://www.maisonethier.com/en/cp-saint-basile-le-grand', None, None, None, 'http://www.tonispetsitters.com', None, None, 'http://fraimandds.com', None, 'http://www.ama.ab.ca', '1592280649', 'http://www.molinascarpetcleaning.com', '1592280653', 'http://www.shipcanada.ca', None, None, None, 'http://www.boosterjuice.com', '1592280661', None, None, None, 'http://www.stanleykingrealtor.com', 'http://www.martinssalon.com', None, 'http://www.autolkn.com', 'http://transformationchurch.tc', 'https://www.staples.com', '1592280679', None, None, 'http://www.stationstreetpgh.com/', None, 'https://www.messagenowpr.com', 'http://www.marybillington.net?cmpid=ul4n_blm_0006', 'http://www.wendys.com', 'https://themobmuseum.org', 'http://www.herbalinfusions.ca', 'http://www.daintycakesbakery.com', None, None, 'http://bionailspa.ca', None, None, 'http://www.burgerinn.com', 'http://www.kitchenstuffplus.com/', None, 'https://www.nandos.ca/eat/restaurants/richmond-hill', '1592280710', None, 'http://www.fivelampschophouse.ca', 'https://www.anytimefitness.com/gyms/2441/Brampton-ON-L6P-2R1/?utm_source=yelp&utm_medium=local', None, 'http://www.jphairdesign.com', None, 'http://chicknribz.com', None, 'http://unclegeorgessprouts.com/', 'http://www.menchies.com/frozen-yogurt-shops/frozen-yogurt-dix--30-qc', 'http://phoenixkitchenandbath.co', None, None, None, 'http://www.jfcsaz.org', 'http://www.quincetoronto.com/', 'http://www.touchmassagestudio.com/', 'http://inyatibedliners.com/', 'http://www.thesuperiordispensary.com', 'http://silvertoncasino.com/dine/best-bars-las-vegas', None, None, None, 'http://razzleberriezyogurt.com/Contact.html', 'http://www.speedyapollo.ca/', 'http://szechuangardenmadison.com', 'http://www.shopjustice.com', None, None, None, 'http://averymoving.ca', None, None, None, None, 'http://www.desertvalleyoralsurgery.com', 'https://www.guardianprotection.com/yelp/2219-2220.aspx?utm_source=profile&utm_medium=yelp&utm_campaign=2018&utm_content=pittsburgh', 'http://www.bosa1.com', None, None, 'http://techparamedics.com', 'http://www.sleekskinaz.com/', None, 'http://www.mesaeastbowl.com', 'https://www.fullcircleautowash.com', 'http://www.billabbottgm.com/?cs:pro=repman&cs:e=yelp', 'https://gomedicalonline.com', None, None, 'http://www.albericisdeli.com/', None, None, 'http://www.oakmontskincare.com', 'http://www.alexanders-photography.com', 'http://www.barberellasalon.com', None, 'http://yourspacesalons.ca/curio', 'http://www.themavericksaloon.com', 'http://www.phoenixcremation.com', None, None, None, None, 'http://www.johnnymalloys.com/default2.htm', 'http://www.shop-haven.com', None, None, 'https://www.valumart.ca/store-locator/?storeId=0449', 'http://www.blumenthalarts.org', None, None, None, None, 'http://www.sameday.ca', None, 'http://www.babydollcoutureglam.com', None, None, 'http://www.jenniferwebdesignlasvegas.com', 'http://robertostacoshop.com', 'http://www.thehotdogstop.com', None, 'http://www.timhortons.com', 'http://oise.library.utoronto.ca', 'https://www.hushxpose.com', None, 'http://www.pittsburghpaintballpark.com', None, None, None, None, None, None, 'http://www.exklusivmotorsports.com/', 'http://ontrac.com', 'http://www.academyinsuranceschools.com', None, None, '1592280863', 'http://locations.arbys.com/us/az/goodyear/442-n-litchfield-rd.html', 'http://www.misoya.ca/', 'http://cloudcryo.com', 'http://www.thaifoodkitchenhenderson.com', None, 'http://www.chiggyonline.com', 'https://www.robiniacourtyard.com', 'http://www.themarlowe.ca/', 'http://www.rushtoescape.com', None, None, None, 'http://www.westmountmoving.com', None, 'http://americantitleserviceagency.com', 'https://jamesheltzeldmd.com', 'http://www.bridaldesires.ca', None, None, None, 'https://bodies-illustrated-tattoo.business.site', None, 'http://www.scottsdaleprincess.com/dining/the-grill', None, None, 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://houseofkabob.ca', 'http://www.idealautobody-lasvegas.com', 'http://www.ballantyneacupuncture.com', '1592280918', 'http://www.creditunion1.org/locations.html?Address=89117&btnSubmit.x=0&btnSubmit.y=0', 'http://www.themintlv.com', '1592280925', None, 'http://www.shogungastonia.com', None, 'http://dabangbistro.com', 'https://hot-pot-restaurant-1236.business.site', None, None, None, 'http://www.bajafresh.com/stores/30407', None, 'http://www.desertrockin.com', None, 'http://www.therosebarandgrille.com', None, None, None, 'http://www.metro.ca', '1592280953', 'http://www.jewelryrepaircleveland.com', 'http://www.elitetaekwondoschool.com/', 'http://mrsub.ca', None, 'http://calibercollision.com/locate-a-caliber-collision-center/las-vegas-downtown/', 'http://www.lunabearstudios.com', 'http://www.southsidecomicspgh.com/', 'https://www.meetyourmechanic.com', None, None, None, None, 'http://www.homewater.com', None, 'https://www.northwestacura.com', None, 'http://brickhousegrill73.com', 'http://www.merrymaids.com/southwest-pennsylvania', 'http://www.savemoresportstore.ca', 'http://www.american-armynavy.com', 'http://www.katysamericanindianarts.com/', None, 'https://www.loandepot.com/branches/Gilbert-AZ?sc_camp=DE925F8ECA0F4E0D8092C7E108A615A3', 'http://wpr.org/zorba/', 'http://www.fountainhillsdentalcare.com/', None, 'http://lanesbakerymadison.com', None, 'https://www.bramptonchryslerdodge.com', 'http://www.theleaguebarbershop.com', 'https://www.chick-fil-a.com/arboretum', 'http://www.swisschalet.com', 'http://www.motdcosmetics.com/', None, None, 'http://www.pizzabogo.com', None, 'http://www.lazeezshawarma.com', 'https://www.servproparmasevenhills.com', None, None, None, None, None, 'http://womenshealthassociatesaz.org', None, 'http://www.peoriakia.com/', 'http://hazelounge.ca', 'https://stores.factory.jcrew.com/en/j-crew-factory-vaughan-mills?srccode=X%7CPMG%7CNaturalSearch%7CLocal%7CYelp%7C441', None, None, 'http://www.beachesjazz.com/', None, 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', None, 'http://fiercegirlfitness.com', 'http://www.pizzapoint.ca/index.html', 'http://www.celinedionlasvegas.com/', 'http://www.saltandpeppercalgary.ca', 'http://www.theplumberguy.com', 'http://www.adair-home.com', None, None, None, 'https://happy-dayz-smoke-vapor-kratom-cbd-shop.business.site', None, 'http://www.greateaglebarandgrill.com', None, 'http://www.azbridestudio.com', 'http://www.rocknrolltattoos.com', 'https://deftcycle.com', 'http://www.homeoutfitters.com', None, None, 'https://local.safeway.com/safeway/az/phoenix/810-e-glendale-ave.html', 'http://www.thelibraryusa.com', 'http://www.markhamauto.com/', None, None, 'http://www.glassbubbleproject.com', None, None, None, 'http://www.icecreamshopwoodbridge.com', 'https://larosh.business.site', None, None, None, None, None, 'http://www.minuteclinic.com', 'https://www.ulta.com/stores/peoria-az-228', 'http://www.fillmorecharlottenc.com', None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, None, 'https://www.moneytreeinc.com/branch/north-nellis', None, 'http://www.allactionplumbing.com/', 'http://www.greenmachinepest.com', 'http://www.mandelgroup.com/apartments/apartment_detail.cfm?n_id=100', None, 'http://manchuwok.com', 'http://www.chocolatemessenger.com', None, 'http://nocoastdiff.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://www.legacywmglv.com', None, 'http://trinitycleveland.org', 'http://www.asahi-net.or.jp/~BV7Y-MRS/ori/', '1592281136', 'http://www.hepaticapgh.com', 'http://www.carzonelv.com/', None, None, None, None, None, 'http://www.mobilemistinglv.com', None, None, None, 'http://www.7-eleven.com/?yelp=35549', 'https://boc.az.gov', None, 'http://www.greatclips.com/salons/3063', 'http://www.chipofftheblocklv.com', None, None, 'http://www.DiscoveryTreks.com', None, None, 'http://www.pinnaclepeakdental.com', None, 'http://www.cartridgeworldusa.com/store20', None, 'https://www.charlottepersonaltrainer.org', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', None, 'http://www.gnc.com', None, None, 'https://crumblcookies.com', None, None, None, None, 'https://thecandlestudio.com', 'http://www.advantageorthotics.net', 'http://www.familyoptometry.net', 'https://www.blindersburgers.com', None, None, None, None, 'http://www.harborfreight.com', 'http://www.fabutan.com', 'http://www.crystalfallspools.com', 'http://www.regency.edu/campus/tolleson/?guest', None, 'http://vegasvalleycarpetrepair.com', None, 'http://www.createacurb.com', 'https://xonailsandspa.com', 'http://www.southwoodrealty.com', 'http://www.quiktrip.com', None, 'http://www.azdoordoctor.com', 'https://www.choicehotels.com/south-carolina/rock-hill/quality-inn-hotels/sc042/rates', 'https://www.nickgravinodds.com/', 'http://www.timhortons.com/', 'http://www.toughlotus.com', 'http://www.paulinacluteevents.com', 'https://www.ediblearrangements.com/stores/6610-E-Baseline-Rd-Mesa-AZ-85206', None, 'http://tandyleather.com', 'http://www.needpoolservice.com', 'http://www.austinfleck.com', None, 'http://www.tlcpetlodge.com', '1592281255', None, None, None, None, 'http://www.seven44.com/birthday-parties/', 'http://www.appliancerepairphoenixforless.com', None, None, 'http://secondchancedoorsaz.com', None, 'http://www.mcfaddensvegas.com', 'http://www.christianpurdie.com', None, None, 'http://www.tacobell.ca', None, None, 'http://www.collinslocksmith.com', None, 'http://www.lucy.com/', 'https://thewingkingcafe.com', 'http://www.josbank.com/AjaxStoreLocatorDisplayView?catalogId=14052&langId=-1&storeId=13452&utm_source=yelp&utm_medium=listing&utm_content=835&utm_campaign=NC', None, 'http://www.clevelandboudoir.com', None, None, 'http://www.gyubeejapanesegrill.com', 'http://www.apsobibi.com', None, None, None, 'http://mentorfamilyfoods.com/', None, None, None, None, 'http://www.rentoffthegrid.com', None, None, None, 'http://www.mojavecoffeeaz.com', None, 'http://www.certifiedluxuryauto.com', 'http://famigliabaldassarre.com/#home', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.insuranceoflasvegas.com/?cmpid=rebq_blm_0006', 'http://www.statelinevapes.com', 'http://www.dignitymemorial.com/funeral-homes/jacksonville-fl/hardage-giddens-town-country-funeral-home/2548', 'http://www.jesterscourttattoos.com', 'http://tastyplattersandfriedchicken.com', None, 'http://www.bignons.com', '1592281334', None, 'http://www.eliteautoworld.com', 'http://www.yorkregiontransit.com', None, None, None, None, None, None, 'http://www.drexylusa.com', 'http://www.craftheating.com', 'http://www.1stinsightinspections.com', 'http://www.aztecarestaurantcharlotte.com', 'http://www.clubevolve.com', None, 'http://www.cgvegas.com', 'http://www.thebarkerlounge.com', None, None, None, None, None, 'http://www.pediatricalliance.com/secondary.aspx?lid=5&id=4&v=1', None, None, None, 'https://www.dominos.com', None, None, '1592281377', 'http://www.studio1250salonspa.com/', None, None, 'http://bocconcino.ca', 'http://www.crashacademylv.com', None, 'http://yourcbdsourcenc.com', None, None, 'http://mod-n-art.blogspot.com', None, None, 'http://www.deskhub.com/scottsdale', None, 'http://www.toronto.ca/parks/prd/facilities/complex/466/index.htm', 'http://hilbishmotor.com/', None, 'http://www.martinsdeli.com', 'http://haddieslv.com', 'http://imperialoutpostgames.blogspot.com/', None, '1592281408', None, None, None, None, 'http://www.scoopspittsburgh.com/', 'http://moios.com', 'http://fourpointstempe.com', None, None, None, None, None, None, None, 'http://www.totalblisssalon.com/', None, 'http://www.dairyqueen.com/ca/', None, None, None, None, 'http://www.metropolitanmarket.com/', 'http://www.uwhealth.org/uw-carbone-cancer-center/cancer/10252', '1592281439', 'http://www.divasxpress.com/', 'https://www.phatridesscottsdale.com', None, None, 'http://www.donleyservice.com/', 'http://mccchurch.org/', 'http://www.rydingautobody.com/', None, 'http://www.ramseyfamilydentistry.com/', 'http://www.thechocolateria.ca', None, None, None, 'https://www.hkseafoodgarden.com', 'http://www.deltaco.com', 'https://thetinfoxrestaurant.com', 'http://www.mygardenfloral.com', None, None, None, None, 'http://www.fwdnightclub.com/', 'http://www.juhllv.com', 'https://stores.bestbuy.com/pa/pittsburgh/473-clairton-blvd-588.html/?loc=ns100&ref=NS', 'https://www.walgreens.com/locator/walgreens-5400+pearl+rd-parma-oh-44129/id=3314', None, 'http://www.kw.com/kw/agent/janice.vidovic', 'http://www.xanmongolianbarbeque.com', None, 'http://www.lapalette.ca/', 'http://www.kalonbeautyboutique.ca', 'http://www.gpcsurgery.com', 'http://matrixphysiotherapy.com', None, 'http://www.strictlydiscs.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700006430627140&ds_s_kwgid=58700000443429122&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', None, 'http://www.vibrantlifestyle.ca', 'http://ardmore.apartments/kingsgrant', 'http://www.quickrepairjewelry.com', 'https://www.solasalonstudios.com/store/atherton_mill', 'http://www.firestone.com', 'http://spice7.ca/', None, None, None, None, None, 'https://www.cafedesamissewickley.com', None, 'https://www.morgan-properties.com/apartments/pa/pittsburgh/club-at-north-hills/', 'http://copperkettlepgh.com', 'http://clearviewfcu.org/', None, '1592281535', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, None, 'http://www.easymovingpro.com', None, None, 'http://www.blackmountaindistillery.com', 'http://www.papiquesoclt.com', 'http://Kensmasonry.com', None, 'https://www.rubytuesday.com/', None, 'http://www.autoshow.ca/', None, None, None, 'https://www.boltbus.com/', 'http://www.natural-medicine.center', 'https://reliablecorporation.com', None, 'http://klausn.com/', 'http://www.3guysoptical.com', None, None, 'https://www.camdenliving.com/scottsdale-az-apartments/camden-san-marcos', None, 'http://www.knockoutmotorcycles.com', None, None, 'http://www.portlypiperpub.com/', None, 'http://www.funlove.com', 'http://spice7.ca/', 'http://www.chatime.com', None, None, 'http://www.serpentiniarena.com', None, None, None, 'http://www.kingputtlv.com/#!henderson/c1wd0', None, 'http://www.thelittlegym.com/airdrieab/pages/default.aspx', None, None, None, None, None, None, None, 'http://www.yourbbqguys.com', 'http://sohosushilounge.com', 'http://local.honeyville.com/tempe-honeyville-store.html', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://www.fwtengbariatrics.com/', None, None, 'http://manesociety.com', 'http://usnwc.org/visit/food-beverage/', 'http://Kristaldentistry.com', 'http://www.bankofamerica.com', None, 'http://www.hontechaz1.com', None, 'http://www.bulletproofoff-road.com', 'http://www.papajohns.com', None, 'https://www.audioexpress.com/locations/7200-w-chandler-blvd-chandler-az-85226/', None, None, None, None, None, 'http://www.fossil.com', None, 'http://lasvegashoa.com', 'http://www.binions.com', 'http://www.hihealth.com/storelocator/view?id=34', None, None, None, None, 'http://www.kelsoelectric.com', 'http://www.emergencyappliancerepairlasvegas.com', None, None, 'http://www.kabob-g.com', 'http://www.balloonking.ca', 'http://dickensmitchener.com', None, None, 'http://www.lubestop.com/Locations/Painesville', 'http://www.purplepestsolutions.com', None, 'http://www.bostonsgourmet.com/', 'https://www.gilbertlawoffice.com', 'http://www.fh.az.gov/', 'http://www.midas.com/phoenix/store.aspx?shopnum=1394&dmanum=684001', 'http://www.nellosscottsdale.com/', 'http://www.radicas.com/', 'http://www.homersservicecenter.tireweb.ezytire.com/', 'http://derryvets.ca', None, 'http://ztejas.com/phoenix-mexican-restaurant', 'http://www.mazdaofrichmondhill.com', 'http://www.illinois.edu/', 'http://www.dunlap-magee.com/', None, 'http://homeswithjean.com', 'http://fareastfootspa.com', None, None, None, 'http://www.darlingdonutsaz.com', 'https://www.take5oilchange.com/locations/oh/northolmsted-135/', None, None, None, None, 'http://www.calltoddbrown.com?cmpid=LTV5_BLM_0006', None, None, None, None, None, 'http://www.dpdough.com', 'http://mackbrosbakerycafe.com', None, None, None, None, 'http://www.makeupbydebbieverver.com', 'http://www.eastsidecannery.com/dining/cannery-row-buffet', 'http://phoenixwineparties.com', 'https://stores.fossil.com/nv/las-vegas/las-vegas-south-premium-outlets-7416/', None, None, None, None, None, None, None, 'http://RdEnvios.net', '1592281777', 'https://spiritsandspice.com', None, None, 'http://www.phoenixbackpain.com/', None, 'http://valeriesfurniture.com/', 'https://denverdefenseusa.com', None, 'http://www.indigo.ca', None, 'https://stores.jcpenney.com/az/goodyear/clothing-stores-goodyear-az-2842.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2842', 'http://www.2toneboxing.com', '1592281801', None, None, None, 'https://www.precisionairandheating.com', None, 'http://thescratchkitchen.ca', 'http://www.thepilatesfirmlasvegas.com', 'https://www.speedycash.com/find-a-store/arizona/phoenix/indian-school-and-16th?utm_source=yelpstorelocator&utm_medium=Affiliate&utm_content=afflink', 'https://dirtdoctorscleaning.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.clubmonaco.ca', None, 'http://www.pearlpoolsandspas.com', 'http://www.thesocialvineyard.com', 'http://www.rmgrealty.com/Arizona/Phoenix/Rent/index_azphx_rent.html', 'http://www.ichibansushi.com', None, None, '1592281831', None, None, 'http://www.brothershvac.net', 'https://thebrassmonkey.us', None, None, 'http://www.kidtokid.com/pittsburgh', 'http://www.acuranorthscottsdale.com', 'http://www.agaveyaguacate.blogspot.com/', 'https://www.hertzcarsales.com/bell-road.htm', None, None, 'http://bostonpizza.com/', 'http://www.jayssprinklers.com/', None, None, None, None, 'https://www.statefarm.com/agent/us/az/mesa/matt-watson-lxwwg8kvlak?cmpid=w32y_blm_0006', None, None, 'https://www.biggusushihouse.ca', '1592281865', 'http://www.loveandsandwiches.com', None, None, 'http://karlscustomdubs.com', 'http://www.thecomputerknight.com/', None, 'http://www.frontgate.com/', 'http://www.pacificeastkent.com', 'http://primarycarechandler.com', None, None, 'http://www.uwhealth.org/locations/detail.jsp?locationId=156', None, 'https://fourseasonsexpresscarwash.com', None, '1592281892', None, 'http://www.petproslv.com/', 'http://www.lomasisalon.com', None, None, None, None, None, 'https://i-love-pho-restaurant.negocio.site', None, None, 'http://www.vincentspizzapark.com/', 'https://trwdayspa.com', None, 'http://www.strosewalkincare.com', 'https://www.hilton.com/en/hotels/phxhyhw-homewood-suites-phoenix-north-happy-valley/?SEO_id=YELP-HW-PHXHYHW', None, 'http://www.carefreeemb.com', None, None, None, None, 'http://www.yourfeelgoodsoap.com', 'http://www.massageoasispro.com', None, 'www.brokenplate.ca', 'http://www.deltaco.com', None, None, None, None, None, None, None, None, None, 'http://pocolocopizza.com', None, None, 'http://www.ladedapitt.com', None, 'http://www.cartersfurniture.com', None, 'http://www.countrystyle.com', None, 'http://allnationsdriving.ca', 'http://www.lasvegas-cars.com', None, None, 'http://www.ashbourneflowers.com', 'http://www.ridleys.com', 'http://www.christenbury.com', 'http://azfibrocenters.com', None, None, None, None, 'http://dramelyoussef.com', None, None, None, None, 'http://kirtlandtavern.com', None, None, 'http://www.freedomboardshop.com', 'http://greenhomecarpetcleaning.com/', None, 'https://locations.traderjoes.com/nv/henderson/97/', '1592281994', 'http://www.rfwash.com/medina', 'http://www.bocktown.com/', '1592282000', 'http://autumnshairstudioaz.com', 'http://jdtowing.mylocalis.com', 'http://www.ipolished.com', 'http://www.meljackson.com', 'http://www.theaveyyc.ca', 'http://www.shobulv.com', 'http://www.labcorp.com', None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://www.jaeger-lecoultre.com/us/en/boutiques/UnitedStates/LasVegas/3104.html', None, 'http://www.libertygrand.com', None, 'http://www.bellocreationsbyti.com', None, None, None, None, None, 'http://thepeppersusa.com', 'https://www.liveoverture.com/communities/las-vegas-alexander', None, 'https://www.uwhealth.org/findadoctor/clinic/135', None, 'http://GreekTable.ca', 'http://www.runforyourlife.com', 'http://www.veronapizza.ca/', 'https://www.get-go.com/', 'http://www.superpizzapgh.com/', None, 'http://mikesdrywallservice.com', None, 'https://www.winners.ca', 'http://tendersteakhouse.ca', None, 'https://www.cleclothingco.com/pages/locations-hours', None, 'http://www.brueggers.com/', None, None, None, None, 'http://www.madisonflorist.net', 'http://valleyspine.net/', None, 'http://www.swisschalet.com', None, 'http://pulpjuiceandsmoothie.com', None, None, 'http://www.lillysgourmetpasta.com', None, 'http://www.darrellsgarage.com', None, 'http://www.americaasia.com', 'http://www.jacquesesilvas.com', None, 'https://www.searsauto.com/stores/2754?psid=campaigncode-2754', 'http://johnnyrockets.com', 'http://www.mysmilesonriggs.com/', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.goldenwestmanagement.com/', 'http://plazabookslasvegas.com/', 'http://www.bistroonlincolnpark.com/', 'http://www.jakesboathouse.com', 'https://www.jazzercise.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Pittsburgh-PA-15206/809058/', 'http://www.walmart.ca/en/walmart-deerfoot-south-supercentre/1089', None, None, None, 'http://www.timhortons.com/ca/en', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.monroyconstruction.com', 'http://innofchagrinfalls.com/', 'http://ifindproperties.com', 'https://elcortezhotelcasino.com/things-to-do/speakeasy-barbershop/', None, None, 'http://www.detroitconeycruiser.com', None, 'http://www.starboardfinancial.com', 'http://www.nailstorylv.com', 'http://www.verizonwireless.com/stores/arizona/avondale/palmilla-204088/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'https://www.gowireless.com/stores/nv/henderson/henderson-lake-mead-crossing/', None, 'http://www.mrosmow.com', 'http://www.pizzaburgh.net/', None, 'http://fourtoronto.com', None, None, 'http://www.fiveguys.com', 'http://www.quiktrip.com', None, None, None, 'http://www.aegcompany.com/', 'http://www.danishpastryhouse.ca', 'http://www.houseoftricks.com/', 'http://www.hoorayforplay.ca', None, None, None, None, None, 'http://storelocator.staples.ca/stores/en_CA/AB/Calgary/132', 'http://www.computation.ca', '1592282183', 'https://painter1.com/las-vegas', 'http://www.everythinggoesaz.com', 'http://www.kravingcatering.com', None, 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'http://www.mrchickencle.com', None, None, 'http://www.victorstire.ca/index.htm', None, 'http://www.firkinpubs.com/firkinonbaystreet/', None, None, None, None, 'http://schuppchiropractic.com', None, 'http://www.fashionnailsbar.com', None, 'http://www.winners.ca', None, 'http://scottsdaletreatment.com/', None, 'http://www.goodfellascollision.com/', 'http://oakparkdeli.com', 'https://www.eswstaffing.com', None, 'http://www.lowes.com', 'http://www.boneyardusa.com/', 'http://whiskeyroseaz.com', 'http://registrystc.com', None, 'http://bpgwi.com', None, 'http://www.bigdogs.com', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85205/218-in-mesa/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-218&utm_content=website-link&howheard=IYE', 'http://www.JimmyJohns.com', 'http://www.gimmeacupcakenc.com', None, None, None, None, None, 'http://www.sallybeauty.com', None, None, None, 'http://www.adeckabove.net', None, 'http://www.cleanfreecarpetcleaning.com/', None, 'https://thehub.lyft.com/hours/ohio', None, 'http://www.secondcup.com', None, None, 'http://www.westshoreprimarycare.com/index.aspx', 'http://www.pfaff.com', None, 'https://joeappelphotography.com', None, 'http://www.mezonaortho.com', 'http://www.westsidemotorsnv.com', 'http://rainbowfoodgo.business.site', 'http://www.eyespyoptometry.com', None, 'https://stores.sunglasshut.com/us/pa/homestead/122-w-bridge-st.html', 'http://www.vipautosales.com', 'http://www.destefinobeautybar.com', 'https://www.gerbercollision.com/locations/champaign-il', None, None, 'http://www.icepicsvideobar.com', 'http://rosegarden.mesacc.edu/index.html', '1592282308', 'http://sonoranpestcontrol.com/', 'http://www.goldengriddlecorp.com', None, None, None, 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1353', 'http://TonyMandarich.com', None, 'http://www.sacredhour.com', None, None, None, 'http://www.bellezabeautylasercenter.com', 'https://www.popcoffeeworks.com', None, 'http://www.lasvegaslifecoach.com', 'http://www.reformedpilates.com', 'http://www.myfoodcity.com/', None, 'http://www.AmandaRoseDance.com', 'http://www.infinitydentaloffice.com', 'http://www.canadiantire.ca/en', None, 'http://www.lululemon.com/vaughan/vaughanmills?cid=yelp', 'http://www.PoopFinders.com', 'https://www.californiaclosets.com/locations/charlotte/charlotte-showroom/?CC5=32008&CC6=30593&utm_source=directory&utm_medium=local&utm_content=NC154-M1-SR1', 'http://tosinosusa.com', 'http://cucinetta.ca', 'https://www.circlek.com/store-locator/us/huntersville/9101-sam-furr-rd/2705102', None, 'http://antrobusdesigns.com/', 'https://locations.jackinthebox.com/us/az/scottsdale/20385-n-hayden-rd', None, 'http://www.nancykhielpc.com', 'http://fancy-taste-of-china.business.site', None, 'https://www.wineonline.ca', None, 'https://www.purolator.com/fr', 'http://www.carpetrestretchrepair.com', None, None, None, None, None, 'http://www.picknsave.com', None, 'http://www.eatzucchini.com', 'http://www.appliancerepair-gilbertaz.com', None, None, 'https://banking.nbarizona.com/blocator/viewLocationMap.html?recordId=186&latitude=33.463873&longitude=-112.344932', None, None, None, 'http://www.alcolandscape.com', 'http://www.phokim88.com', 'http://www.on-sitevideo.com/', None, 'http://azboatcovers.com', 'http://www.3guysoptical.com', 'http://www.doctoroo.com', None, 'http://speakeasysuncity.com', None, None, 'https://www.calgarycoop.com', None, 'http://pizza.dominos.ca/Calgary-Alberta-10108', None, None, 'http://phoenixnorth.place.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_phxzn_en_homepage_desktop&code=YB', None, 'http://porzia.ca', 'http://www.hometownurgentcare.com/parma/', None, None, 'http://www.whasn.com', 'http://www.spypilates.com', 'http://www.thepearlofasia.com', 'http://www.nocauptown.com', None, None, None, None, None, None, None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/1/?utm_source=yelp&utm_medium=listing&utm_campaign=website', None, 'http://www.firstresponsesecuritylv.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281358086&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, '1592282443', None, 'http://ravengp.com', None, 'http://www.nickmayerlincolnmayfield.com', None, None, 'https://www.extravaganzaflorist.ca/?srccode=yelp_track', 'http://www.venturawebdesign.com', 'https://www.goldencorral.com/locations/2449/golden-corral-e-franklin-blvd', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/27713+Lorain+Road+Corner+Of+Porter+Road-North+Olmsted-OH-44070/storeid=2587?cid=ps_ylp_2020', 'http://www.barriocantina.com', None, 'http://cedarvillageapartments.ambz.com/', 'http://www.pacificharborssunrise.com/?=yelp_track', None, None, None, 'http://www.accidentlawyers-nevada.com/', 'http://www.greatclips.com/salons/3063', 'http://www.pittmanautomotive.com/', 'http://alobobatempe.com/', 'http://www.robinsontowncentre.com', 'http://www.livsalades.com', None, 'http://www.glamourco.com', None, 'http://www.table17.ca/', 'https://www.walmart.com/store/2768/mesa-az/details', 'http://therabbitspot.com/the-peculiar-rabbit/', None, 'http://industriapizzeria.com/restaurant/carrefour-laval-laval-qc/', None, 'http://solidgreenlandscaping.com', None, None, None, 'http://www.jodyberger.com', 'http://pittsburgh.madscience.org/', None, 'http://www.studio103fitness.com', 'http://www.aztecabakeries.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://www.empirekent.com', None, None, 'http://www.haircutmenqueensway427etobicokeon.ca', None, 'http://painreleasetherapy.com', 'https://www.doughopkins.com', None, 'http://www.chevron.com', 'https://www.cubesmart.com/arizona-self-storage/phoenix-self-storage/72.html?utm_source=yelp&utm_medium=ccpc&utm_campaign=ppct', None, 'http://www.twistgallery.ca/', 'http://www.timhortons.com/', 'http://locations.qdoba.com/2303/?utm_source=Yelp_Listings', None, None, 'http://fareastexpress.weebly.com', 'http://www.chevron.com', 'http://www.theultimateplumber.com', 'http://www.lvmannequins.com', None, '1592282555', 'http://www.freshii.com', 'http://www.rumbi.com', 'http://www.gymnastics702.com', None, None, 'https://www.staples.com', 'http://perfectbalancecharlotte.com', None, None, None, None, 'http://www.mecklenburgfootandankle.com', None, None, None, None, None, 'https://shopdelysees.com', 'http://RyanAlexander.us', 'http://www.bigdogsbrews.com/', 'https://arizonaflooringstore.com', 'http://walmart-eyedocs-lasvegas.com/SpringMtn-Rainbow', None, 'http://www.holyhillac.com', None, 'http://www.edojapan.com/locations/ca/ab/10/calgary-airport-yyc-calgary-ab', None, 'http://www.greatclips.com/salons/2507', 'http://www.blackboxfix.com', 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', 'http://www.kidville.ca', None, 'http://www.gatewaycalgary.ca/', None, None, '1592282615', None, None, 'https://www.walgreens.com/locator/walgreens-11001+s+eastern+ave-henderson-nv-89052/id=6545', None, 'http://www.pneuunik.com', None, None, None, 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.azfamilydentist.com', None, 'http://www.rockanddock.com', 'http://www.bedbathandbeyond.com', None, None, None, 'http://www.ncbcmedspa.com/', 'http://www.storysbuilding.com/cocktail-parlor/', 'http://www.superiorscooter.com', 'https://www.redlobster.com/locations/list/nv/north-las-vegas/1870-w-craig-road', 'http://www.911bug.com', None, 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', None, None, 'http://www.lushusa.com/', None, 'http://www.sheridannurseries.com/stores/mississauga_oakville_garden_centre', None, 'https://arielsscottsdale.com', 'http://winchesterkitchen.com', None, None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280197189&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://madisonwest.thegreatframeup.com', '1592282679', 'http://www.lidocafe.ca/', None, 'http://www.madisontailor.com', 'https://www.caesars.com/flamingo-las-vegas/things-to-do/wildlife-habitat?utm_campaign=Yelp&utm_term=WildlifeHabitat&utm_medium=local&utm_source=yelp&utm_content=attraction', 'http://www.redoyourpool.com', 'http://metzfabindustries.com', None, 'http://www.cjsw.com/', 'https://pompeiis.com', None, None, 'http://spicebox.illinois.edu/', None, None, None, 'http://www.frenchfryheaven.com', None, None, None, None, 'http://www.dentistryofthecarolinas.com', 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://www.coolcuts4kids.com/salondetail/default.asp?salonid=66009', 'https://www.jerseymikes.com/7029', None, None, None, None, None, 'http://www.secretshairsalon.com', None, None, None, 'http://www.marcos.com/', 'https://www.smalv.com/OurCenters/ConvenientCares', None, None, None, 'http://www.tuckersparts.com', None, None, None, None, None, 'http://holyjoeshalalmeats.com', None, 'https://locations.sonicdrivein.com/oh/parma/1842-snow-road.html', 'http://www.francescascollections.com', None, None, None, None, 'http://www.copperstartrans.com', None, None, None, 'https://www.shopwss.com', 'http://kraft.com/', 'http://shef1.com', 'http://noblesmokebarbecue.com', None, 'http://www.rossstores.com', 'https://millersalehouse.com/locations/Las-Vegas/?utm_source=Yelp&utm_campaign=Yelp', 'http://westgateohio.com', None, None, None, None, None, None, None, 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', None, 'http://www.lush.ca', 'http://www.vapingxtreme.com', None, None, 'http://www.sleepinn.com/hotel-huntersville-north-carolina-NC316?source=pmfyelp&pmf=yelp', None, None, None, None, None, 'http://www.cashamerica.com/SUPERPAWN-stores/NV/LASVEGAS/LV12', 'https://www.lifespine.life', None, 'http://www.kitchencharm.ca', 'http://reservedesignstudio.com', None, 'https://www.goodwillaz.org', 'http://www.feastonbrilliant.com/', 'https://www.walgreens.com/locator/walgreens-1250+tom+hall+st-fort+mill-sc-29715/id=11968', '1592282823', 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID675', 'http://www.spaworkssupply.com', None, 'http://www.bayviewsevenanimalhospital.ca', '1592282832', 'http://www.pearlharborgiftshop.com', 'http://www.racewaycarwash.com', None, None, None, 'http://www.dryospur.com', 'https://pizzeria1081.com', 'http://www.sapporopittsburgh.com', 'http://sassynailbar.com', 'http://locations.einsteinbros.com/az/scottsdale/6501-e-greenway-pkwy-bldg-5.html?utm_source=storelocator', 'http://www.torreyanalv.com?campaign_code=yelp_Torreyana_NV_89118', None, None, None, 'http://amchiropracticlv.com', 'http://www.tutortime.com/your-local-school/gilbert-az-6066/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, None, 'http://www.incredibleindiafood.com', None, 'http://www.fairviewcycle.com', None, None, None, 'http://www.uppercrustpizza-lasvegas.com/', None, None, 'https://www.pizzahut.ca/#!/home', 'http://hwy55.com', 'http://www.arizonaaesthetics.com', 'https://zoomrentals.com/toronto-airport-car-rentals', None, None, 'http://www.captiverooms.com', None, None, 'http://www.simons.ca/simons/article/article.jsp?artId=22822', None, None, 'https://heroburgers.com/locations/yonge-sheppard/', 'http://www.gardunosofarizona.com', None, 'http://www.a2zmobiledetail.com', None, None, None, None, None, None, None, None, 'https://locations.panerabread.com/oh/mentor/9587-mentor-avenue.html', 'http://www.rossstores.com', None, None, None, None, None, 'http://www.myarizonawatertech.com', 'https://www.dominos.com', None, None, '1592282926', 'http://www.kitchenstuffplus.com', None, 'http://www.eggsquis.com/en/restaurants.php?restaurant=st-hubert', 'http://www.eleganza-boutique.com', 'http://titansgym.com/contact/mentor-2', None, None, None, 'http://www.stapletonroofing.com/', 'http://www.ollyfrescos.ca', 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', None, 'http://www.dollar.com', None, 'http://www.homebirthlasvegas.com', None, None, 'http://www.krazykatskc.com', None, 'http://www.bebe.com', None, None, None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYULCC', 'http://www.pinklime.com', None, None, None, 'http://www.paradisebuilderslasvegas.com', None, None, 'http://azvetdentists.com/index.php', 'http://www.divinespa.ca', 'http://www.scorpiusdance.com/', 'https://empoweredlifestores.com', None, None, None, 'http://www.thebigbox.ca', 'https://www.speedyfurniture.com/speedy-furniture-of-lower-burrell/', None, 'http://www.kayserford.net', None, '1592282990', None, 'https://www.nuvisionautoglass.com', None, None, None, None, None, 'http://www.compressionmanagement.com', None, 'http://www.accentuatedbydiana.com', 'http://www.boardandbrush.com/scottsdale', None, None, 'http://awolin.com', 'https://petpausecharlotte.com', None, 'http://www.freddiesii.com', None, None, 'http://www.greenleafsalads.com/green-leafs-restaurants.aspx', 'http://hotbeansvegan.net', None, 'http://www.haddoxandsons.com', 'https://www.halibuthouse.ca', 'http://www.quiktrip.com/', None, 'http://www.mogadrivingschool.ca', None, None, 'https://stores.hallmark.com/nv/lasvegas/amys-hallmark-shop-lasvegas-nv-19403.html', None, None, None, None, 'https://ad.doubleclick.net/ddm/clk/434417653;234991578;u', None, 'https://powerrdfarmersmarket.com', None, 'http://www.squirrelhillphysicaltherapy.com/', None, None, None, 'https://www.downtownmedipedi.com', 'http://mikesbarbershops.com/', None, None, None, 'https://www.checkcity.com/locations/nevada/mall-ring-circle-and-galleria-mall/', None, None, 'http://www.greatclips.com/salons/6225', None, None, 'http://www.lvdiscountmattress.com', None, None, 'http://www.hmonglegacymarket.com', None, None, None, None, None, None, 'http://www.rooterandplumbingservice.com', 'http://www.morrisonresidential.com/', 'https://www.scaleandfeather.com', None, None, None, 'http://www.redrockspringswater.com', None, 'http://simplysuperiorwclv.com', 'http://broadwaycarwash.com/', None, None, None, None, None, 'https://www.seeadvanced.com', 'http://www.prmpointevista.com', None, 'http://www.mikescomputerrescue.com', None, 'http://www.fourseasons.com/lasvegas/spa.html', 'http://villagepubcasino.com', None, None, 'http://optimalptlv.com', None, 'https://www.planetfitness.com/gyms/copley-fairlawn-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://barre3.com/chandler', 'http://www.sonicdrivein.com/', None, None, None, 'http://www.datadoctors.com/locations/102', None, 'http://www.bedo.ca', 'http://southcharlotte.mosquitojoe.com', '1592283125', None, 'http://www.vansandwich.com', None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, None, 'http://www.autoillusions.com', None, None, '1592283139', 'http://paradisedoggrooming.com', 'http://www.chauhansindiancuisine.com', None, 'https://thevendordepot.com', 'https://www.pgatoursuperstore.com', None, 'https://www.MarbleRoomSushi.com', None, '1592283154', None, 'http://americanplg.com/', None, None, 'https://www.scottsdaleloancompany.com', None, None, None, 'https://www.classaxethrowing.com/tempe/', 'http://www.motosierrallc.com', None, None, None, 'http://www.lakewooddentaloffice.com', 'http://professionalclean2.biz', 'http://www.goldenview.ca', None, None, 'http://www.coach.com', None, None, 'https://www.azure9cle.com', 'http://EatRburgers.com', None, 'http://www.museumdental.ca', None, 'http://www.dollargeneral.com', None, None, 'http://www.slnailspa.com', None, None, None, 'http://www.mesaaz.gov/police', 'http://v95winelounge.com/', None, 'http://www.motorcarstoyota.com', None, 'http://www.humbertosmexfood.com', 'http://www.arpheating.com', 'https://www.hiexvaughan.com/?utm_source=yelp&utm_medium=referral', 'http://www.haggen.com', 'http://www.structube.com', 'http://www.southendpainting.com', None, None, 'http://sinaloarestaurant.com', None, 'http://trooseveltstavern.com', None, 'http://www.ozziesfurnishings.com/', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'http://www.jkknowslvhomes.com/', None, None, None, 'http://arizonaima.com/', None, None, 'http://www.rockandchalk.com', 'http://www.manuelscatering.com', '1592283250', '1592283252', None, None, None, 'https://locations.paychex.com/us/arizona/phoenix', None, 'http://www.mtroniks.com', None, 'http://www.acehelpful.com', 'http://www.tarosfish.com', 'https://www.plazaexecutive.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=KL%20execsuite', None, 'http://pumpernickels.ca/index.php', None, '1592283272', None, None, 'https://azvent.com', None, 'https://local.firestonecompleteautocare.com/arizona/scottsdale/13802-n-scottsdale-rd', None, 'http://chandlerfamilydentist.com', 'http://www.rbspizza.com', None, None, 'http://robertostacoshop.com', None, 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', None, None, 'http://www.banfield.com/veterinarians/nc/charlotte/bky?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://www.coppas.com/nonna-francesca-ristorante/', 'http://www.firstclassmoving.com', None, None, None, None, 'http://www.salonsafari.com', None, None, None, 'http://www.injanation.com', None, None, 'https://locations.theupsstore.com/az/mesa/2753-e-broadway-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, None, 'http://www.katsurdentalaz.com', None, None, None, 'http://www.goziptow.com', 'http://www.nothingbutnoodles.com', 'https://thewoodlawn.pub', 'https://www.interiorgardenslv.com', 'http://gabbys.ca', None, 'http://www.allfamilydentist.com/index.html', None, None, 'http://www.allpetsvc.com', 'https://myrosatis.com/peoriaolive/', None, 'http://www.manzanitaballclub.com', 'https://www.krown.com/canada/ontario/scarborough/scarboroughstclair/', None, 'http://www.bodytherapycalgary.com', 'https://www.jasonsdeli.com/restaurants/scottsdale-deli', 'http://kidstoothdrs.com', '1592283362', 'http://www.nuworldgraphicslv.com', None, 'http://www.congeewong.com/', None, None, 'https://locations.dollartree.com/ca/paradise/2140/', 'http://www.nvoandp.com/', None, None, None, 'http://proficient-landscape.business.site', None, None, 'http://www.cavecreekoutfitters.com/', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.ronmarhofernissan.com', None, None, None, 'http://www.mldocs.com', 'http://www.princessbeautyspaa.com', 'https://locations.jackinthebox.com/us/az/scottsdale/20385-n-hayden-rd', 'http://www.seventhsisterbakery.ca/', 'https://nowtoronto.com', None, 'http://www.practical-art.com', 'http://kidtokid.com/charlotte', '1592283413', None, 'http://phoenixazacupuncture.com/', 'http://www.countryinns.com/elyriaoh', None, None, 'http://www.osakes.com', None, 'http://www.goldenstatestorage.com/self-storage/nv/henderson/best-storage', 'http://fourteenestates.com', None, 'https://www.pittsburghcocktailbar.com', None, 'http://adlercpa.com', 'http://orientalbuffetaz.com/', '1592283437', None, 'http://www.fryteamaz.com/', 'http://www.knitonestitchtoo.com', 'http://www.taipei-fc.com/', None, 'http://www.countrydayscornmaze.com', 'http://hamptoninn3.hilton.com/en/hotels/alberta/hampton-inn-by-hilton-calgary-airport-north-YYCAPHX/index.html?SEO_id=YELP-HP-YYCAPHX', 'https://partsworxs.com', None, 'http://www.midas.com/charlotte/store.aspx?shopnum=3255&dmanum=184', None, None, None, 'http://www.speedway.com', None, 'http://www.lakesidegreens.com', None, None, None, 'https://lebanon-express.business.site', None, None, None, 'http://www.bonniegordoncollege.com', 'http://www.brueggers.com/', 'http://www.hamiltonsonthesquare.com', 'http://www.equestrianapartments.com/', None, 'http://www.gr8fuldeli.com', 'http://www.bk.com', None, 'http://www.swirlitfroyo.com', 'http://sweethouselv.com', 'http://www.thebasementarcadebar.com', None, None, 'https://www.supercuts.com/locations/on/toronto/leaside-village-haircuts-57027.html', 'http://www.fujicomfort.com', 'http://www.mesasecurestorage.com', None, None, None, 'https://order.subway.com/Default.aspx', None, 'https://las-vegas-real-estate-authority.com', 'http://www.azsneeze.com', None, 'http://www.communitymanagementaz.com', 'http://www.casareys.com', None, None, 'https://grandmasdogdaycare.com', None, 'http://www.einsteinbros.com', None, None, None, None, 'http://www.desertwindharley.com', 'http://www.methodpgh.com', None, None, 'http://www.tbbs.ca/', None, 'http://www.bravo-bistro.ca', 'https://phenixsalonsuites.com/professional_detail_page/?professional_id=9596', 'http://www.festivallatinoamericano.org/', None, 'http://www.davescosmicsubs.com', 'http://www.surgecafe.com', 'http://findyourcenter.com/things-to-do/signature-event/1/blues-b', 'http://juaninamill.com', None, None, 'http://www.simplygreekfood.com', 'http://cruzinreubenz.weebly.com/', 'http://www.classicattic.biz', None, None, 'http://5anddiner.com/', 'http://www.arbys.com', '1592283561', None, None, None, None, 'http://www.envymodelmanagement.com', None, 'https://www.trixpestmanagement.com/contact/', 'http://www.acehardware.com/store-details/15943', 'http://www.bridalelegant.com', 'https://local.fedex.com/pa/monroeville/office-4993/', None, 'http://www.steljescardiology.com', None, 'http://tddental.ca', None, None, 'http://www.rebeloil.com', None, None, None, None, None, None, None, 'http://www.dizengoff.ca', None, None, 'http://www.toysrus.ca', None, 'http://www.harkeytileandstone.com', None, None, None, None, None, None, None, None, None, 'http://shoponthehill.com', None, None, 'http://katespade.com', None, 'http://executiveofficesuitesscottsdale.com/', 'http://www.seedentist.com', None, 'http://www.thegaleteam.com', 'http://www.jubileedonuts.com', None, 'http://www.bk.com', 'http://coronadocare.com', None, None, 'http://delightcleaners.com', 'http://www.bk.com', 'http://sunnyslope.guhsdaz.org', 'http://www.gamaclean.com', None, 'http://www.mercurylock.com/', 'http://www.hickoryheightsgc.com', None, 'https://local.lenscrafters.ca/on/scarborough/300-borough-drive.html', None, 'http://www.frangipane.ca/', 'http://www.countrystyle.com/', 'http://www.romanoscafe.com', 'http://www.hanchao.ca', None, 'https://www.sephora.com/happening/stores/toronto-eaton-centre', None, 'http://koolsvilletattoos.com', None, 'http://www.realtyonegroup.com/', None, None, 'http://www.phxburritohouse.com', 'http://nrgballroom.com', 'http://subway.com/', None, None, 'http://www.phoenixseminary.edu', 'http://www.theonesushicalgary.ca/', None, 'http://www.beautifulfloors.com', None, None, None, 'http://stanstowinginc.com', None, None, 'http://www.goodlifefitness.com', None, None, None, 'http://leesliquorlv.com/locations/sunset-office/', None, 'http://alwaysbff.com', 'http://www.hyperionfinancial.com', None, None, None, 'http://www.SavvyCollector.com', None, 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', None, 'http://www.Janddfitness.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.batteriesplus.com/store-locator/oh/akron-montrose/batteries-plus-165?utm_source=yelp&utm_medium=local&storecode=165', None, None, None, 'https://www.wyndhamhotels.com/hotel/17885?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:17885', 'http://www.therowdyboutique.com', 'http://shadysidesmiles.com', 'http://www.ballyfitness.com/get-started/guest-pass/free-guest-pass.aspx?CID=SM:Yelp:7-dayGP:BasicListing:2009', None, 'http://southcltspa.com', None, 'http://www.goldenhouserestaurant.com/', None, None, '1592283737', None, 'http://www.sportsclubatcitysquare.com', None, 'http://Autolika.net', None, None, 'http://brimhalleyecenter.com', 'http://sunvalleybumper.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.youcallweinstallflooring.com', None, 'http://www.bargaincentralwarehouse.com', None, 'http://massageschampaignil.net', None, 'http://www.arentwenaughty.com', 'http://www.deltaco.com', None, 'http://www.spectrumcafe1.com', 'http://www.markbeam.massagetherapy.com', 'https://www.buckeyeflorist.com', 'http://www.torontoacademyofacting.com', 'http://www.roncyvillagevetclinic.com', None, None, None, 'http://worldwiderv.com', None, None, None, None, None, None, None, None, 'http://harbhair.com', 'http://www.grassrootsaz.com/', None, None, None, None, 'http://www.calgary.ca/CSPS/Parks/Pages/Locations/SW-parks/Edworthy-Park.aspx', 'http://www.arizonabeekings.com', 'http://www.eggsmart.ca', None, 'http://www.fitness365.ca', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', None, '1592283810', 'https://www.avis.com', None, None, None, 'http://phpphotography360.com/', 'https://www.sephora.com/happening/stores/toronto-eaton-centre', 'http://www.leositaliansocial.com', 'http://www.TKTeam.us', None, 'http://www.laviniarestaurant.com', None, 'http://www.marshallscanada.ca', 'http://www.levantcharlotte.com', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'http://www.bermanmovers.com', None, None, 'http://www.massimodutti.com', None, 'https://www.circlinghawkfarm.com', 'http://www.smileconceptsaz.com', '1592283845', 'http://youdirtydoglv.com', None, None, 'http://www.azbattlezone.com', 'http://www.WobbleToTs.com', 'http://www.chocolatsfavoris.com', None, None, None, None, None, 'http://nolmstedoh.vacation.travelleaders.com/', 'https://www.walgreens.com/locator/walgreens-6101+andrews+rd-mentor+on+the+lake-oh-44060/id=5820', None, None, None, None, None, 'http://www.infocuseye.com', 'http://www.wyattworksclt.com', 'http://www.amazelv.com', 'https://www.nationalcarsaleslv.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.loveboutiqueonline.com', 'http://www.theedgeoneuclid.com', None, 'http://www.MotorcycleTraining.com', 'http://www.artisanarmorcoat.com', 'http://www.goldenchinarancho.com', None, 'http://www.oldcountrybuffet.com', 'http://www.jdm-ottawa.com', 'http://www.kinder-prep.com', None, None, 'http://thelookbyannieb.com', 'http://edwinsbutchershop.org', 'http://ontarioplace.com/en/vistaeatery/', None, None, 'https://silverleafrealty.chime.me', None, None, None, 'http://chadavegas.com', 'http://www.drwilsongyn.com', None, None, 'http://nestorslandscaping.business.site', None, None, 'http://www.chevron.com', None, None, None, 'http://www.xlash.ca', 'https://chavelosrestaurant.com', 'http://thegoodeggaz.com/', None, None, 'https://www.choicehotels.com/CN568?mc=blypypaf', None, 'https://stores.nordstromrack.com/us/az/peoria/7535-w-bell-rd?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=388&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', 'https://demetres.com/locations/shops-at-don-mills/', 'https://www.tommyguns.com/ca/location/calgary-southcentre-mall/', 'https://sundevildining.asu.edu/hours-and-locations/tempe/hassayampa', None, 'http://www.happypetvet.com', None, 'https://locations.mrtire.com/oh/medina/5847-wooster-pike?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.vivedecor.net/', 'http://www.bastoneauto.com', None, None, None, None, None, None, None, 'http://cheetahslasvegas.com/', None, None, None, None, 'http://thepeoplesdutchpot.com', 'http://canisrestaurant.com', 'http://www.blackcreekbrewery.ca/', 'http://hwy55.com', None, None, 'http://tinanailspa.com/', 'http://dellingerwrecker.com', 'http://www.pchelpforce.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, None, None, None, None, None, 'http://www.ddsdiscounts.com', None, 'http://spacevintageclothing.blogspot.ca', 'http://www.handelsicecream.com', None, 'http://www.markanthonypainting.com', None, 'http://www.cnbcomputers.com', 'https://villaggio-natural-nails-spa.business.site', None, 'http://www.maidpro.com/east-valley/', None, None, 'http://www.knightsonguard.com/', None, None, 'http://www.peccoledental.com/', None, 'http://www.proformancehealthaz.com', 'http://robertostacoshop.com', None, None, 'http://www.roomwhite.com/', 'http://www.burlandjewelry.com', None, 'http://www.jcuts702.tumblr.com', None, None, None, None, 'http://cashwells.com', 'https://www.chick-fil-a.com/monroe', None, None, None, None, 'https://www.target.com/sl/fairlawn/986', 'http://www.renue-spa.com', None, None, 'http://cementtileshop.com', None, 'http://www.coppas.com', None, None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.pausebeauty.com', 'http://www.sushijun.ca', None, None, None, None, None, None, None, 'https://www.stayalfred.com/property/stay-alfred-at-the-venue/?utm_source=Yelp&utm_medium=Pittsburgh&utm_campaign=The_Venue', 'http://daishinsteakhouse.com', None, None, None, None, 'http://www.tagura.com', None, None, None, 'http://good2gopizzalasvegas.planetcafepages.site', None, 'http://www.specialtyvehicles.com', '1592284096', None, None, None, None, 'http://www.theworkroom.ca', '1592284105', None, 'http://blackmagictattooaz.com', 'http://www.Orcatek.com', None, 'https://chadani.ca', None, None, None, None, None, 'http://petsafariaz.com/', 'http://www.bohemianstylehouse.com', None, None, 'https://www.cubersgolfcars.com', None, None, None, 'http://nationsfreshfoods.ca', 'https://www.enterprise.com/en/car-rental/locations/us/pa/bedford-ford-4039.html?mcid=iyp:8368400', 'https://www.homedepot.com/l/S-Boulevard-Charlotte/NC/Charlotte/28217/3646?cm_mmc=seo-yelp&', 'http://Axaresurfacingllc.com', 'http://www.getglamoureyes.com', 'https://www.sephora.com/happening/stores/toronto-eaton-centre', 'http://www.landscaperecyclingcenter.org', 'http://www.crossroadslv.org', 'http://deepblueaquarium.net', '1592284148', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.angryshrimpshack.com', 'http://www.drfinkelmd.com', 'http://www.confideroofing.com', 'http://www.rona.ca/en/Rona-lentrepot-st-laurent-saint-laurent', None, None, 'http://www.ilovefetch.com', None, 'http://www.timhortons.com/', None, 'http://www.reddevilrestaurant.com', None, None, 'http://www.chocolate76.com', None, None, 'http://www.powerupchiropractic.com/', 'http://bettysbombassburgerscle.com', 'http://www.acerentacar.com/landing/Canada/Calgary/Calgary-Intl-Airport.aspx', None, 'http://eastofchicago.hungerrush.com', 'http://www.whitesbrakeandwheel.com', None, 'http://www.vintagevideocanada.com/', None, 'http://www.allcreaturesah.com', None, None, 'http://www.limobusters.com', 'http://acdelcoau.to/n8qk', None, None, None, None, 'https://sheadentalaz.com', 'http://lamaisonpham.com', None, 'http://all-aroundmovers.com/', None, None, '1592284214', None, None, None, None, 'http://www.thaimeuppittsburgh.com', None, None, 'http://www.cherryberryyogurtbar.com', 'http://www.cashamerica.com/SUPERPAWN-stores/AZ/PHOENIX/Tem01', 'http://www.evenstevens.com', 'https://funkatronicrex.games', 'http://www.dunkindonuts.com', None, None, 'http://obgynofphoenix.com', 'http://www.friendlys.com', 'https://www.uhaul.com/Locations/Self-Storage-near-Las-Vegas-NV-89169/047537/', 'http://www.markyandsparkys.com/', 'http://www.globalpetfoodstoronto.ca/locations/beaches/', 'https://www.clubpilates.com/chandler', 'http://www.windowgang.com/Cabarrus-County-NC/window-gang-of-cabarrus-county-nc.html?lid=1041', 'http://www.distinctdetailaz.com', None, None, 'http://www.holycrossway.org', 'http://www.yoloyogurtlove.com/', 'http://maps.concentra.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://smartstopselfstorage.com/storage-locations/usa/nevada/las-vegas/smartstop-self-storage-4851-e-bonanza-rd', None, 'http://www.nicastrospub.com/', 'http://www.thecircleofhealth.ca', 'http://hotovenbakery.com/location_cloverdale.html', None, None, 'http://gustiitaliangrill.com/', 'http://www.baseballheritagemuseum.com', None, None, 'http://www.medleycarpetcare.com', 'https://www.westerndental.com/en-us/find-a-location/arizona/phoenix/13651-n-35th-ave', 'http://www.ralphlauren.com', None, None, None, 'http://www.calgaryagemanagement.com', None, None, 'http://www.lennar.com/New-Homes/Arizona/Phoenix/Chandler/Layton-Lakes-Chandler?utm_source=Yelp&utm_medium=Social&utm_campaign=CORPLEN_Yelp_Listings', 'http://www.dermal360.com', 'https://www.maids.com/161/?utm_source=Yelp', 'https://www.choicehotels.com/wisconsin/stoughton/quality-inn-hotels/wi075/rates', None, None, 'https://www.arizonafansandblindsgilbert.com', 'http://www.chinobandido.com', 'http://www.desertjewelapts.com/', 'http://www.eyecareforanimals.com/location/?utm_source=yelp&utm_medium=Business&utm_campaign=EyeCareforAnimalsScottsdale-ScheduleAppointment', None, 'https://flynnaudio.com', None, 'http://www.tropicalsmoothiecafe.com', None, '1592284306', None, 'http://www.djseanvanhorn.webs.com', 'http://mycharlottefence.com', None, 'http://www.renovatuschurch.com', 'http://www.fiorittodental.com', 'http://nevadasolargroup.com', None, None, None, 'https://www.dickeys.com', None, None, 'https://www.chuys.com/locations/north-carolina/charlotte', None, 'https://www.hilton.com/en/hotels/cltsphx-hampton-suites-charlotte-south-park-at-phillips-place/?SEO_id=YELP-HP-CLTSPHX', None, 'https://socialinnovation.org/location/192-spadina/', 'http://www.greatclips.com/salons/3063', None, 'https://www.azipc.com', None, None, 'http://www.justtemptations.com', None, 'http://fourseasonshs.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'https://doudsveterinaryhospital.com', None, None, None, None, None, 'https://www.staples.com', '1592284360', None, 'http://www.montereydental.ca', None, None, None, None, None, 'http://themaidsofconcordnc.com/', None, None, 'http://www.fluidmartialarts.com', None, '1592284382', None, 'https://www.thedrybar.com/locations/las-vegas-in-the-cosmopolitan/?utm_source=yelp&utm_medium=locations&utm_campaign=nv_vegas-cosmo&utm_content=h', 'http://www.cinemahair.com', None, 'http://oasisoutdoor.com', None, None, None, None, 'http://www.lasvegasdyno.com', 'http://www.boraliato.com', 'http://www.kyleishea.com', 'http://www.audioexpress.com', '1592284404', 'http://www.midtownimports.net', None, 'http://www.centropizza.ca', 'http://www.yogaloft.ca', None, 'http://bodyandsoulclinic.ca', 'http://www.apexsystemsinc.com/about/locations.asp?o=AZ&m=21', 'https://locations.pitapitusa.com/ll/US/OH/Mentor/7519-Mentor-Ave', None, 'http://www.Southhillsjewelers.com', 'http://www.tradesource.net', 'http://www.stvincentdepaul.net', 'http://malthousetavern.com/', 'http://www.ntb.com/store/8656/matthews-nc-28105-4502?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'http://Westmorelandpoolservice.com', None, 'http://www.simmonsfarm.com', None, None, 'http://www.laysalterations.com', None, None, 'https://www.midfirst.com/', 'http://www.7-eleven.com/?yelp=29384', 'http://superstitionhobbies.com', None, None, 'https://www.creativekidslearningcenter.com/schools/las-vegas-nv-6708/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhancedprofile', 'http://topspizzasouth.com', 'http://www.fiascogelato.com/', 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', 'http://sunwinchinesefood.com/', None, None, 'https://www.bannerhealth.com/locations/gilbert/banner-children-s-banner-health-clinic', 'http://www.raisetheroot.ca', 'http://elmanantial1.com', None, None, None, 'https://www.ctrlv.ca/ctrl-v-north-york-downsview', 'https://www.enterprise.com/en/car-rental/locations/us/ky/henderson-5842.html?mcid=iyp:8368400', None, 'http://www.classiccarslasvegas.com', None, 'http://www.exoticlimoslasvegas.com', None, None, 'https://haircutmenstrongsvilleoh.com', 'http://www.computech-auto.com', None, None, None, None, None, None, None, 'https://www.nemacolinwoof.com/mcmurray-pet-resort-spa/', None, 'http://www.m3vnailbar.com', None, 'http://www.doetschoffroad.com', None, 'http://gilbertinternalmedicine.com', 'http://www.sitinbangkok.com', None, None, 'http://cyclemotive.com/', 'https://www.industriousoffice.com/scottsdale/fashion-square', None, 'http://www.kalifano.com/', 'http://www.rocketfizz.com', 'http://www.tempe.gov/city-hall/city-court', 'http://www.goodwillsp.org/shop/retail-stores/pineville/', None, None, 'http://www.azoresautogroup.com', 'http://www.thepassenger.co/', None, 'http://www.westernfencecompany.net/', None, 'https://locations.tgifridays.com/oh/copley/125-montrose-west-ave.html', 'http://www.grill4u.ca/', 'http://azchildrenssafari.com', None, None, None, None, 'http://www.unionstationtaphouse.com/', None, None, None, None, 'http://orchidnailspalasvegas.com', None, 'http://www.happynoodle.ca', None, None, None, None, None, None, 'http://www.wambamfence.com', None, '1592284562', 'http://www.bankofamerica.com', 'http://www.vegasorientalrugcleaners.com', None, None, 'http://sait.ca/highwood', 'http://www.postalconnectionswi.com', None, None, None, None, None, None, 'https://www.loblaws.ca/store-locator/Loblaws+-+Moore+Avenue/1155?storeId=1155', None, None, 'https://www.villagetrattoria.ca', None, None, 'https://www.choicehotels.com/arizona/tempe/comfort-suites-hotels/az020/rates', 'http://www.southpointcasino.com/entertainment/weekly.php', 'https://brooklyn-mikes.business.site', 'http://worldnailspachampaign.com', 'http://www.mayoclinic.org/departments-centers/general-internal-medicine/primary-care-arizona/overview', None, None, 'http://www.ezpawn.com', None, 'http://www.peselectro.com', 'http://walkerautoandtruck.com/', None, None, 'http://digitell.com', None, None, 'http://www.alaskanquality.com', None, 'http://www.spa4-paws.net', 'http://www.yarnsunlimitedpa.com', None, 'https://www.mcdonalds.com/us/en-us/full-menu/123dollarmenu.html?cid=PS:GCM_MOP:NB::Yelp:All', 'http://www.vodaspainc.ca/', None, None, 'http://www.calvarytricity.com', 'https://www.alberta-king-of-subs.com', None, 'http://www.studiotaylorsalon.com', 'http://www.alfredservice.com', 'http://www.magnusonhotels.com/Magnuson-Hotel-Papago-Inn', None, 'http://www.lasvegaszoo.com', 'http://www.javaden1022.com', None, None, '1592284652', 'http://www.amadeuspatisserie.com', 'https://forumnailsgilbert.com', None, None, None, None, None, 'http://axxiopizza.com/', 'http://campuspointekent.com', 'https://barrospizza.com', 'http://www.darrenkwik.com', None, 'http://www.Functionalintegratedtraining.Com/', None, None, 'http://www.spiritoftheking.com', 'http://www.dragonflyhotyoga.com', 'https://www.grovedeervalley.com', 'http://www.batteryparkwinebar.com', None, 'http://www.berkshireway.com', None, 'http://www.moccobistro.com', None, None, None, None, None, None, None, None, None, 'http://www.afancypupharrisburgnc.com', 'http://www.thebugguylucas.com', 'http://azbreastfeeds.com', 'http://www.starbucks.com/store/10759/', None, 'http://www.lavenderspaandnailsalon.com', None, None, 'http://www.lifestylestaffing.com/', 'http://www.timhortons.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'https://www.thebiermarkt.com/fr/locations/montreal.html', None, None, 'http://findlaykia.com', 'https://www.janasbakery.com', 'https://www.tortaselchavoaz.com', 'https://www.dieselbarbershop.com/location/mcdowell-mountain-village', 'http://yelp.com/elite', None, None, 'http://www.rebeloil.com', None, None, None, None, None, 'https://www1.shoppersdrugmart.ca/en/store-locator/store/1268?back_to=%2Fstores%2Frichmond+hill%2C+on+l4c+1v7', None, 'https://www.petsmart.com/stores/us/nv/north-las-vegas-store1896.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://azcentralfoodandwine.com', 'http://premierparkingusa.com/airport-parking/phoenix-sky-harbor/howard-johnson-phoenix-airport', None, None, None, 'http://www.kibosushi.com', None, 'https://tanrepublic.com', None, 'http://www.dalhousievet.com', None, 'https://infinityheatingandcooling.com', 'https://www.homedepot.com/l/Pecos/NV/Las-Vegas/89120/3316?cm_mmc=seo-yelp&', None, None, 'http://www.theboxdonut.com', None, 'http://www.peelspas.com/', None, None, 'http://onestopnutrition.com', 'http://www.allstatetransmission.net', '1592284784', 'http://number1signs.net', 'http://www.teamzornek.com?cmpid=p8i6_blm_0006', None, None, 'https://www.lilicafepgh.com', None, None, 'https://www.palmtrees-r-us.com', None, None, '1592284801', None, None, 'http://www.browsersden.com', 'http://www.duffsfamouswings.ca', None, None, 'http://store-locator.barnesandnoble.com/store/2772', 'http://www.timhortons.com', None, None, None, 'http://www.oldtowngringos.com', None, 'https://fixautousa.com/north-scottsdale', 'https://www.reesepromovers.com', 'http://www.dsw.com', 'http://www.mypiada.com', 'http://mirvish.com', None, 'https://www.noahseventvenue.com/north-carolina/traditional/charlotte/', 'https://locations.massageenvy.com/pennsylvania/pittsburgh/791-providence-blvd.html', None, None, None, None, None, 'http://www.anemoneflowers.ca?=yelp_track?srccode=yelp_track', '1592284842', None, 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', None, 'http://KidsRKidslv.com', None, None, 'http://www.shingarusa.com/#!beauty_care/cfvg', None, 'http://neurocenterlv.com', 'http://www.industrialshoecompany.com/', 'https://www.fringesalonaz.com/brijette-risola', 'http://foreignfix.com', 'https://xtndcase.com/pages/about-us?contact_posted=true#contact_form', None, 'http://thenoshaz.com', None, None, None, None, None, None, None, None, None, 'https://www.signaturestyle.com/locations/wi/deforest/cost-cutters-deforest-towne-center-haircuts-17400.html', 'http://www.priorityplumbing.ca', None, None, 'http://www.storage-solutions.org/self-storage/chandler-az-79825', 'https://arizona.weidner.com/apartments/az/phoenix/cobalt-on-32nd-street/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.womensspecialtycare.com', 'http://www.bk.com', None, 'http://www.dickblick.com/stores/nevada/lasvegas/', 'http://kerthinsurance.com', None, None, None, None, None, 'http://www.littlecaesars.com', 'http://www.thebesttattooshop.com', 'http://www.azteendriving.net', 'http://thedragon.ca', None, None, 'http://showmars.com/locations/fort-mill-hwy-521', None, 'http://www.phxdraincleaning.com', None, None, None, None, 'http://www.venue104.com', None, None, None, None, None, None, None, 'http://sumoboysushi.com/home.html', None, '1592284940', 'http://www.feetbegood.com', None, None, 'http://paulsimonco.com/', None, None, None, 'https://www.walgreens.com/locator/walgreens-9166+state+route+43-streetsboro-oh-44241/id=9346', None, 'https://dorianscuttingedge.business.site', None, 'http://www.semisportmed.com', 'http://www.3guysoptical.com', None, 'http://www.woodysburgers.ca', 'http://www.oliviasat53.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360246&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', None, 'http://www.themanestudioaz.com', 'http://www.JimmyJohns.com', None, 'http://www.7-eleven.com/?yelp=29384', None, 'https://www.bobevans.com/our-restaurants/locations/28?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', None, 'http://ufcgym.com/mesa/?utm_campaign=WebHomepageRefID34504&utm_medium=Display&utm_source=Yelp', 'http://nevadahealthcoop.org', None, 'http://www.starbucks.com/store/10759/', None, None, None, None, '1592284990', 'http://www.crumplumbing.com/', '1592284995', None, None, None, None, 'https://www.solismammo.com/arizona/phoenix-central/', None, 'http://www.avondale-dental.com', None, 'http://www.luxesalon.biz/', 'http://www.arbys.com', None, None, 'http://www.inncahootsbarandgrill.com', None, None, 'http://www.annapoornastore.com/', 'http://www.pvhomed.com', 'http://www.obfy.net', 'http://www.kirklands.com/custserv/store.jsp?storeName=Pecan%20Promenade', None, None, None, 'http://www.breezewoodgardens.com', None, None, None, '1592285031', None, None, 'http://cafecocoro.ca', 'https://www.plannedparenthood.org/health-center/arizona/tempe/85283/new-tempe-regional-health-center-4256-90030?utm_campaign=new-tempe-regional-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', None, 'http://www.especially4pets.com', 'http://www.signarama.com/az-phoenix-arcadia', None, 'http://www.sportclips.ca', 'http://twohippiesscottsdale.com', 'http://kindredspiritsanimalhospital.com', None, None, 'https://www.flavorgrilleakron.com', 'https://zionpondcare.com', None, None, None, None, None, 'http://www.stemcellpowernow.com', 'http://www.starbucks.com/store/10759/', 'http://www.indiantrailhardware.doitbest.com', None, None, 'https://marketmalloptometry.ca', None, 'http://www.eastboundbeer.com', 'http://www.myfoodcity.com', '1592285078', 'http://stumppro.com', None, 'http://www.papajoesfishnque.com/', None, None, 'http://www.freerangebrewing.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'https://www1.shoppersdrugmart.ca', 'http://www.darkstarmountaintours.com', None, None, '1592285098', 'http://www.healthforlifend.com', None, None, None, 'http://www.leegardenspadina.ca/', 'http://www.circlekontario.ca/store-locator/ca/maple/1500-major-mackenzie-dr-w/52485', 'http://www.champssports.com', 'http://www.gcugolf.com', None, 'http://agclasvegas.com', None, None, None, 'http://www.ride-faster.com', 'https://weedsgg.ca', 'http://cuppa-tea.ca', 'http://www.pitrobotrepair.com/', None, None, None, 'http://www.scottsdaletint.com', None, 'http://www.christopheramirasalon.com/site/', 'http://ilovefatox.com', 'http://www.northcoasteyecare.com', 'http://www.golfsmith.com', 'https://mabugeneration.com', 'http://www.ossobucco.ca', 'http://www.sears.com', None, None, 'http://www.changevegas.com', 'http://www.kidsfirstdental.com', None, 'http://www.thed.com/', None, None, None, 'http://carlscakes.net', '1592285165', 'http://www.trouvehome.com/', None, 'http://leesatamember.com/locations/chandler/', 'https://www.newmanarmsvegas.com', 'https://www.goldencorral.com/locations/2609/golden-corral-e-independence-blvd', None, 'http://www.justsmilesvegas.com/', None, 'http://www.bespressobar.com', 'http://www.mattressfirm.com', None, None, 'https://www.suntrust.com/branch/nc/charlotte/28269/mallard-creek', None, 'http://frostyroll.ca/index.html', 'http://www.handymannync.com', None, 'http://www.menchies.ca/frozen-yogurt-shops/frozen-yogurt-centropolis-qc', None, None, 'http://www.manulifecentre.com/', 'http://www.wexfordvet.com', None, None, 'http://koryo.ca', None, None, 'http://www.massage1.com/locations/henderson', None, 'http://www.piranhavegas.com', 'https://www.sephora.com/happening/stores/pointe-claire', None, 'http://www.artisticedgesalon.com', 'http://www.azablemovers.com', 'http://www.theparkridge.com', 'http://www.arthurmurray.net', 'http://www.igloofoodequipment.com', 'http://statewidelighting.com', None, 'http://www.bloomskincare.net', None, 'https://autowhiplashrehab.com', None, 'https://www.bigguyspizzaandpasta.com/', None, None, None, 'http://www.restaurantnewverdun.ca', None, 'http://www.strongsvillemassage.com/', None, None, 'http://www.holistic-service.com', None, 'http://www.akrongeneral.org/lifestyles', 'http://www.gorilla-cafe.com', None, 'http://sunsethillsapts.com', None, 'http://www.lasvegasplumbinginc.com/', None, 'http://www.performancehealth.org', None, None, None, None, None, None, None, None, None, '1592285275', 'http://www.tridenthealthcenter.com', None, None, None, None, 'http://www.carlsjr.com', None, None, None, None, None, None, 'http://www.scoutconsignment.com', None, 'http://www.subarucalgary.com', 'http://www.rapidcarelasvegas.com', None, None, 'https://www.petsmart.com/stores/us/ca/concord-store0061.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://www.choicehotels.com/ohio/medina/quality-inn-hotels/oh325/rates', 'http://www.hpb.com/042', 'http://kohtao.ca/', None, 'http://www.lasxpress.com', None, None, None, 'http://www.customfoodservice.com/', None, None, None, None, None, None, None, None, 'http://www.drpatti.com', None, None, None, 'http://www.ampedsoundandcinema.com', None, None, None, None, 'https://www.umcsn.com/Quick-Cares/Quick-Care-Locations-Enterprise.aspx?intMenuID=112&intPageID=191', None, 'http://minus-417.com/spa/', None, 'https://www.redrobin.com', 'http://www.sectionhairstudio.com', '1592285349', 'http://www.lcbo.com', None, 'http://crclasvegas.com', 'http://lacollinaitalianrestaurant.com', None, 'https://www.sprint.com/storefronts/bd/sprint-tempe-az-85282-fcs-519/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.wayo.ca', None, 'http://www.lavishbeautyloungesalon.com', None, None, 'http://stores.bestbuy.com/261/', '1592285368', 'http://www.getyinzguys.com', None, None, None, 'https://locations.checkers.com/nv/las-vegas/4175-e-desert-inn-rd/?utm_source=Yelp', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.NSCCleaningPhx.com', 'https://compadresgrillohio.com/contact-northfield/', None, 'http://www.sunrun.com/solar-by-state/nv?utm_source=yelp&utm_medium=social+media&utm_campaign=Las+Vegas+NY&utm_content=business+url', None, None, 'https://www.hungryhowies.com/store/hungry-howies-01811?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=01811&utm_content=Website_Link', None, 'https://www.ihg.com/crowneplaza/hotels/fr/fr/montreal/yulap/hoteldetail/dining', None, 'http://www.myspace.com/downstairsfashion', None, 'http://azarthritis.com/', '1592285399', 'https://www.karsensgrill.net', None, 'https://www.metro.ca/en/find-a-grocery/312', None, 'http://www.geico.com', None, None, None, 'https://www.wyndhamhotels.com/hotel/15427?tel=18002521709&iata=00093785&cid=fe:ra:20161215:yl:pp:ramus:15427', 'http://www.crownroofing.ca', 'http://www.shoelessjoes.ca', 'http://www.glowblo.com', None, 'http://www.drbjarnason.com', None, None, 'http://www.usiinc.com/find-a-branch/all-branch-locations/usi-silver-state/', 'https://www.huntington.com/Community/branch-info?locationId=23468', 'http://www.yokososteakhouse.com', None, None, None, 'http://agrafineindiancuisine.ca', 'http://www.smokemodernbbq.com/locations/smoke-birkdale-village/', 'http://www.wholefoodsmarket.com/stores/camelback', 'http://www.legionsgames.com/', None, 'http://www.lee-lawfirm.com', 'http://www.solcrossfit.com/home', 'http://www.humberlanddental.com', 'http://www.somethingsbrewingcafe.com/', 'http://www.pizzanova.com/locations/mississauga.html', 'http://www.canigetaruffruff.com', None, 'http://arriviste.coffee', None, 'https://www.tacosmiranchitomexicangrill.com', None, 'http://www.beglamhair.com', 'https://www.skinnymechocolate.com', None, None, None, 'http://www.droog.com/las-vegas/', 'http://www.chevronwithtechron.com', 'https://www.eatmoltobene.com', None, None, None, 'https://www.petsmart.ca/stores/ca/on/richmond-hill-store1403.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', None, 'http://www.alteredegosalon.com', None, None, None, None, 'http://www.electrichaventattoo.com', 'https://www.fergusonfamilymedicine.com', None, 'http://ontariofreshandtasty.com', 'http://www.therockstore.ca/', None, 'http://madison.jiffylube.com/Locations/Store/913/6519-UNIVERSITY-AVE-MIDDLETON-WI-53562-3419', None, 'http://sunstonedental.com/', 'http://www.eddystonemeats.com/', None, None, None, None, 'http://www.thaioneon.ca/', 'http://www.royalhighlandsdental.com', 'http://www.vaughankidsdaycare.ca', None, None, 'http://www.americasbestvalueinnmesa.com', None, 'http://www.slidefoodcart.com/', 'https://locations.jackinthebox.com/us/nc/charlotte/7725-pineville-matthews-rd', None, None, None, None, None, 'https://www.burlington.com/store-details-Store-982--1965-N-Pebble-Creek-Parkway--Goodyear--AZ--85395.aspx?from=85395&id=953966a1-9f02-4594-a04e-279fed1fa6c6', 'https://www.sherwin-williams.com/store-locator/paint-store/avondale/az/1588', 'http://mayuripalaceaz.com', None, 'http://www.lakovagymnastics.com', None, None, None, None, None, None, 'http://www.dynamitegrill.com', 'https://www.jerseymikes.com/3183', 'http://southpointcasino.com/dining/big-sur-oyster-bar?cid=ypbsy', 'http://www.harryrosen.com/store/Chinook%20Centre', 'http://www.thunderbirdtrophies.com', 'http://broadwaycleaners.ca', None, 'https://www.luckmancleveland.com/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Lease%20Up', 'http://www.pacificeastsolon.com/', None, 'https://palmbeachtan.com/locations/NC/Matthews-Matthews-Township-Parkway/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=AUG', None, None, '1592285571', None, 'http://www.lvmaterialhandling.com', None, 'http://www.rosecitykitchen.com/', 'http://www.viecafe.ca', None, None, None, 'http://www.acehardware.com/mystore/index.jsp?store=14692&saddr=43.0709333,-89.32743909999999(53716)&daddr=43.0836,-89.3229(209%20Cottage%20Grove%20Rd%20Madison,%20WI%2053716)', 'http://www.brickartmasonry.com', '1592285585', 'http://kangarooexpress.com', 'https://www.inthenikoftime.ca', '1592285592', 'http://www.anbautomotive.com', '1592285596', None, 'http://www.estatesatwesternairelasvegas.com', 'http://a1sweets.com/scarbrough/index.html', None, None, 'http://www.hibberdorthodontics.com', 'http://www.cowtownguitars.com', 'http://www.pizzamilano.net/', None, None, None, None, None, None, 'http://www.thecookiebarlv.com', 'http://jackastors.com/location-map/25/', 'http://prodigylearningcenter.net', 'http://www.tropicalsmoothie.com/', None, None, 'http://dotsanddoodlesart.com/open-studio/hours/', 'http://www.roobargrill.com', 'http://www.brianhorine.com?cmpid=RKSH_BLM_0006', '1592285633', None, 'http://www.countryblossomflorist.com', 'http://www.9round.com/', None, None, 'https://www.solasalonstudios.com/locations/paradise-valley-village', 'http://nicolesellsvegas.com', None, None, None, 'https://locations.chipotle.com/pa/murrysville/4899-william-penn-hwy?utm_source=yelp&utm_medium=yext&utm_campaign=yext_listings', None, 'https://johansendentalaz.com', 'http://www.edgeworthclub.com', 'http://www.torontopubliclibrary.ca/hou_az_ag.jsp', 'http://www.cage.ca/lasalle', None, 'https://www.mysodalicious.com', 'http://www.witchesandcowboys.com', 'http://www.hcanteen.com', 'http://www.nevadaballet.com/', '1592285669', None, None, None, 'http://www.fallspcclinic.com', 'http://www.checkeredflagplumbingco.com', 'https://locations.vitaminshoppe.com/ca/glendale/vitamins-supplements-glendale-ca-216.html', 'http://highlifesmokes.net', None, 'https://www.papersource.com/locations/az_scottsdale.html', 'http://www.airparkmotorcars.com', None, None, 'http://www.shuttlemoving.com', None, None, None, 'http://www.envirotekhomecare.com', None, None, None, 'http://meltdowncheesery.ca', None, 'https://www.pedrosglendaleaz.com', None, None, 'http://www.besttours.com', 'http://www.arrowheadmontessori.com', None, None, 'http://thomasdentalphx.com', None, 'http://ncct.on.ca', 'http://www.zimbrickhonda.com', 'https://www.glowmedispa.ca/contact/markham', 'http://www.dakotabar.com', 'http://www.sojourndeli.com/', 'http://www.cuttingedgecutleryco.com/our-calgary-location.html', 'http://www.casadelsolepizza.com', 'https://www.glendaleglassaz.com', 'http://www.patisserielacigogne.com', None, 'http://ashbaclothing.com', None, 'http://brewgentlemen.com', 'http://www.dignityhealth.org/urgentcare/az', None, 'http://www.sunflowergifts.ca', None, 'http://www.greatclips.com/', 'http://countryclubautospalv.com', 'https://www.xiexiebodyworks.com', None, 'http://www.centrocafe.ca', 'https://www.comebuytoronto.com/menu', 'http://www.meatballz.net', 'http://www.barkgallery.com', 'http://2topiacycles.com', 'https://www.jackinthebox.com/locations/1541', None, 'http://www.clerkofcourt.maricopa.gov/ne_court.asp', None, 'https://cyclebar.com/location/north-hills', None, 'http://labambaburritos.com/', 'http://divine-nails-spa.com', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'http://www.dunkindonuts.com', 'http://www.pizzazrestaurantpa.com/', None, 'http://www.anthi.ca/', 'https://www.kesssleepingbeauty.com', None, None, 'https://tools.usps.com/go/POLocatorDetailsAction!input.action?locationType=po&locationTypeQ=po&radius=20&locationID=1368675', 'http://www.yinschinesephoenix.com', 'http://www.SUMCooperativepreschool.org', '1592285805', None, 'http://www.bufords.kitchen/locations/moon-township/', 'https://saltoftheearthpgh.com', 'http://www.gotfrogurt.com/', 'http://www.elburritolocollc.com/index.html', None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/5/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://vaporice.com', None, 'http://www.theboulders.com', 'http://www.edicine.com', 'http://www.santorinirestaurant.com', None, 'http://www.dragosisters.com', None, None, 'http://mastercraftcreations.com', 'https://www.camelbackvw.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://spruceitupgardencentre.com', 'https://www.fatcatsfun.com/mesa', None, 'http://www.stardust-country.com', None, None, 'http://www.energiaathletics.com/', 'https://www.thebrick.com/pages/store-vaughan', 'http://www.chaska.com', None, None, None, 'http://www.nulookfloorlv.com', None, None, None, 'https://stores.fossil.com/az/chandler/chandler-fashion-center-8239/', None, None, None, 'http://www.menchies.com/', None, None, 'http://chagrinoutdoors.com', 'http://www.nvgeneral.com', 'http://www.dunkindonuts.com', None, None, None, None, None, None, None, 'http://www.vegasbeadshoppe.com', None, None, 'http://riggsfamilydental.com', None, 'http://www.scottsdalefinejewelers.com', None, None, None, 'https://www.mattressfirm.com/stores/az/mesa/mattress-stores-mesa-az-85206-6956.html', 'http://cielocharlotte.com/', '1592285894', 'http://www.lindsaysautoservice.com/', None, 'http://kims-alterations.com/', None, 'http://www.coreshopping.ca/', None, 'http://www.medinamowershop.com', 'http://glistenupaz.com', None, 'http://www.downeasthome.com', None, None, 'https://www.beachwoodplace.com/en/directory/brigade-13781.html', None, 'http://www.captaintalltale.com', None, 'https://affderm.com/locations/ahwatukee/', None, None, 'http://www.rednails2.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://www.amlautoservice.com/', 'http://www.tungschineserestaurant.com', None, None, None, 'http://www.kravmagatoronto.com/', None, None, 'http://www.icebergdriveinn.com', None, None, 'http://www.hinasushi.com', 'http://www.JimmyJohns.com', None, 'http://www.infocuseyecarelv.com', None, 'http://www.safeway.ca', None, None, None, 'http://www.sunnydawnjohnston.com', None, None, 'http://www.goodlifefitness.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.ickisticki.com', None, None, 'http://www.ghost-armor.com', 'http://www.mycopyexpress.com', 'http://www.sageapthomes.com', 'http://thecarwashbutler.com/', None, 'http://www.sugarcafepittsburgh.com/', 'http://www.waldmandental.com', 'http://www.labcorp.com', None, 'http://www.perfectnailslv.com', 'http://www.lcbo.com', None, 'http://www.pinkynails.ca', None, None, None, None, None, '1592285996', 'https://www.sunburstshutterslasvegas.com/?utm_campaign=yelp+ads&utm_medium=paid+social&utm_souce=yelp', None, '1592286002', None, None, None, 'http://www.lakemetroparks.com/select-park/fairport.shtml', 'https://www.wyndhamhotels.com/hotel/14959?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:14959', 'http://www.captainsbaseball.com', None, 'http://www.surfcitysqueeze.com', None, None, None, 'http://musicmakerscalgary.com', 'http://www.capsuletoronto.com', 'http://www.cakesandribbon.com', 'https://www.bigtroublepizza.com', None, 'http://www.burgerking.ca', 'http://www.kensingtonmidwives.ca', 'http://www.zoomroomonline.com/location/charlotte/', 'https://www.druryhotels.com/locations/phoenix-az/drury-inn-and-suites-phoenix-chandler-fashion-center', None, 'https://www.nordstromrack.com', 'http://jimsparadisecreations.com/', '1592286039', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.safedoggy.com', None, 'http://tasteofgreekscottsdale.com/index.html', None, None, 'http://elmanantial1.com', 'http://www.asics.com/us/en-us', 'http://www.fxfitnessclubs.com/broadview-heights', 'http://galleriartframe.com', None, None, '1592286060', None, 'http://www.arizonapaintingcompany.com', None, None, None, 'http://www.bloombakeshop.com', 'https://daisyfamilyhealth.com', 'http://wolfsonautomotive.com', 'http://www.eddysdelionline.com', None, None, 'http://locations.michaels.com/OH/FAIRLAWN/2745/', 'http://www.liveatcarlyletownhomes.com', None, 'http://www.gymboree.com', None, None, 'http://pandachefwoksushi.ca', None, 'http://icecreamsammies.com', 'http://shearosefarm.com', None, 'http://www.lasvegasbikefest.com/', None, 'http://www.7-eleven.com/?yelp=35583', 'http://www.gianteagle.com', 'http://www.papajohns.com', None, None, 'http://www.ihop.com', 'http://nailbarlv.com/', None, None, None, 'https://www.chick-fil-a.com/arboretum', None, 'http://www.reflectionshairspa.com', None, None, None, None, 'http://www.prettyinminklashes.com', None, 'http://www.walgreens.com/locator/Walgreens-108-GREENSBURG-RD-LOWER-BURRELL-PA-15068/id=11697', None, None, 'http://wunderlichchiro.com', 'http://www.debbiekennedyevents.com', 'http://www.samarakitchen.ca', None, 'http://www.watertectucson.com', 'http://www.ginobros.com', 'http://www.petlandhenderson.org', 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', None, 'http://locations.harristeeter.com/sc/fort-mill/82/', None, None, 'http://www.dagina.ca', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', None, 'http://www.carpet-cleaning-las-vegas.com/index.html', None, 'http://www.deserteyecarelv.com', None, None, None, None, None, 'http://www.truevalue.com', None, 'http://www.mrstucco.ca', None, 'http://newmarketautobody.org', None, None, 'http://jewelsbygdo.com/', 'http://graphicimaging.net', None, None, None, 'http://www.integrativechironc.com', '1592286177', 'http://www.wecareurgentcare.com/', None, None, 'http://www.yarldosacorner.ca', None, None, None, 'http://www.molnarstamp-coin.com', None, None, 'http://www.saharafamilyskinclinic.com/', 'http://redsquarelasvegas.com/', None, None, 'https://gohoneyhut.com', 'http://www.arizonaartsupply.com', None, None, None, None, None, None, 'http://www.hastingsbarbershop.com', None, 'http://www.oxfordmedicalimaging.ca/our-locations/', 'http://laparrillasuiza.com/', None, 'http://www.homeandawayyyc.com', None, None, 'http://www.wendys.com', None, None, 'http://hillsidedentalfineart.com/', None, None, 'http://www.draganhair.com/', 'http://www.charleysplace.net/', 'http://wesa.fm/', 'http://kupfertandkim.com/', None, None, None, 'http://www.stirlingclublv.com', 'http://www.madisonscuba.com', None, None, 'http://www.kaleidoscopejuice.com/', 'http://www.azcarpetcloseouts.com', None, None, None, 'http://www.tuckersmarketplace.ca/', 'http://cfcomputerstore.com', 'http://www.frysfood.com', 'http://www.knochesbutchershop.com/', None, 'http://www.greatclips.com', 'http://www.axeandhatchet.com', 'http://www.factoryshoe.ca', 'http://getmelted.ca/', 'http://Www.saffronpig.com', 'http://www.staircaseflorist.com', None, 'http://www.kreatestudio.com', None, None, 'http://www.BarringtonPlaceWestlake.com', None, 'http://www.apwhc.com', 'https://www.steaknshake.com/locations/oh-elyria-abbe-road/', '1592286278', 'http://howiets.ca', None, 'http://www.progressivehealthctr.com', None, 'http://www.cashamerica.com/superpawn-stores/nv/lasvegas/lv15', None, None, None, None, 'http://blackcatcostumes.com/store/', 'http://www.pacificmist.org/', 'http://www.bankofamerica.com', None, None, None, None, 'http://www.aioli.ca', 'http://tortaselreyphoenix.com', 'http://www.lenhartsace.com', 'http://www.mwuanimalhealth.com', 'http://www.ngstudio.ca', 'http://www.iconsignstores.com', None, 'http://thehydrantonline.com', None, None, 'http://www.sandwichclub2go.com/', None, None, None, None, '1592286333', 'http://www.zoup.com/menu.html?location=ZOU00189', None, None, None, None, None, 'http://www.carolinashealthcare.org/urgent-care', None, 'https://melrosevintagemarket.com', None, None, None, '1592286349', '1592286351', 'http://www.puttingedge.com/vaughan/?utm_source=yelp&utm_medium=cpc&utm_campaign=book_a_tee_time&utm_content=website_link', 'http://www.devillecoffee.ca/', 'http://www.cogeco.ca', None, None, None, 'http://www.totalwine.com/store-info/arizona-tempe-emerald-center/1004', 'http://www.dunkindonuts.com', None, 'http://www.LambsAutoBody.com', 'http://www.westsidemarket.org/vendor.aspx?id=88', None, 'https://www.victoriassecret.com/store-locator#/store/1459', None, None, None, 'http://www.welcometohost.com', 'https://store.vioc.com/ky/henderson/189-north-garden-mile-road-42420-ID0010', 'http://www.sears.com/stores/arizona/mesa/0001628.html', None, None, None, 'http://www.punchysdiner.com/', None, 'https://www.cricketwireless.com', 'http://www.hrpregnancy.com', 'http://www.valero.com', None, None, 'http://www.phxsprinkler.com', 'https://skinlaundry.com/blogs/arizona/scottsdale', None, 'http://www.zippyshelloflasvegas.com', None, 'http://www.clevelandindoorairsoft.com/', 'http://www.quiktrip.com', 'http://www.hannahnailsaz.com/home.html', None, None, None, 'https://www.pghcitypaper.com', None, 'http://www.caffeartigiano.com', None, 'http://www.drinkanddial.ca/', None, None, 'http://www.interiorblue.com/index.html', None, None, 'http://www.marshallsonline.com', None, 'http://www.shell.ca/en_ca', None, None, None, 'http://www.emilys.ca', 'http://fitnessconnection.com/clubs/uptown/', 'https://www.walgreens.com/locator/walgreens-663+e+aurora+rd-macedonia-oh-44056/id=7719', 'https://www.cramptonteam.com', None, 'http://www.greatclips.com', None, None, None, None, 'http://www.IwantActionNow.com', 'http://www.sushimugen.com', 'http://www.oldstonechurch.org', None, None, None, 'http://KinfolkOptimalLiving.com', 'http://www.tjmaxx.com/', None, 'http://www.thetangerinecafe.com/home.html', 'http://inateijapanesecuisine.com', None, 'http://www.themadcactus.com/', None, None, None, '1592286479', 'http://scott-twp.com/pool-hours', None, None, None, 'https://fixautousa.com/phoenix/', None, None, None, None, 'https://changintime.com', 'http://www.sunpointeapartments.net', 'http://www.treasureslasvegas.com', 'http://www.trinityirishpub.ca/', None, 'http://www.bmvbooks.com/', None, 'http://www.azfoot.com/', None, None, 'https://loustivoligardens.wixsite.com/mysite-1', None, 'http://www.visionaryprinting.com', None, None, 'http://nirosgyrosuniversityave.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___phoenix', None, 'http://mullinsapartments.com', '1592286529', 'http://marcos.com', 'http://www.lynegiroux.com/', None, 'http://www.frogspt.com', 'http://www.silverfoxlimos.com', 'http://www.proclipusa.com', None, 'http://www.desertsolutions.com', 'http://www.weissguysaz.com', None, None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'https://www.nationalcar.ca/en/car-rental/locations/ca/qc/montreal-trudeau-airport-c7n1.html?mcid=iyp:8368400', None, 'http://www.dollargeneral.com/', None, 'http://crossfitblade.com/crossfit-blade-main', 'http://www.brazilbakery.ca/', 'http://www.nealsyardremedies.ca', None, None, None, 'http://www.simpsonpropertygroup.com/apartments/chandler-arizona/coronado-crossing-chandler?vrurl=yelp.com', None, '1592286564', None, None, None, 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', None, 'http://www.blindstogo.com/en/stores/north-york?ua=North+York%2C+ON+M6A+2T4%2C+Canada&rds=25', 'https://www.thedrybar.com/locations/las-vegas-in-miracle-mile/?utm_source=yelp&utm_medium=locations&utm_campaign=nv_vegas-miracle-mile&utm_content=h', None, 'http://www.allaboutpeople.net/locations/phoenix-az/', 'http://www.thewirelesscenter.com', None, 'http://www.gamestop.com', 'https://www.nanakflights.com', None, None, None, 'http://www.kareyskitchen.com', 'https://middletonframing.com', 'http://www.accurateleakdetection.com', None, 'https://hornetmovingnc.com/?utm_source=Yelp&utm_campaign=Yelp', None, 'https://www.PrattsPets.com', 'http://www.lechateau.com/style/index.jsp', 'http://www.honuintegrativehealing.com', None, None, None, 'http://losprados-golf.com/', 'http://www.blendmenshair.com', 'http://www.truehomeac.com/', None, None, 'http://www.aaahousecleaners.com', 'http://www.butlermortgage.ca/', 'http://www.bulliesbbq.com', None, None, 'https://www.livehunterschasewestlake.com', 'http://www.sammysburgers.com', None, 'http://www.paulfrank.com', 'http://honeybeebakery.org', 'http://hairbyheatheraz.com', None, None, None, 'https://elementsmassage.com/middletonwi', 'http://dodaspizza.com', None, 'http://makeupbyangelinamaria.com', 'http://www.lastminutemovers.ca', 'https://local.safeway.com/safeway/az/mesa/3622-e-southern-ave.html', None, None, 'https://locations.wendys.com/united-states/oh/cleveland-heights/13246-cedar-road', 'http://mannysbarber.com', 'http://www.happytailsbarkery.co', None, 'http://searsauto.com', None, None, 'http://www.artbox.co.kr', 'http://www.mriofarizona.com/', 'http://www.cuttinedgebarber.com/', 'http://dollbarinc.com', 'http://www.unhookedrecovery.com/', 'http://www.shell.us', None, None, 'http://www.perfectdimensionsaz.com', None, 'http://www.secretosbeautysalon.com', None, 'http://www.dinerscorner.com', 'https://elementsfitnessstudios.com', 'http://www.thecitadelleplaza.com', 'http://www.elevationpdr.com', None, 'http://secondcup.com', None, 'http://catspjscatsitting.com', None, 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_964', 'http://www.cashmerecricket.com/', None, 'https://www.thaicoconutaz.com', None, None, None, None, 'http://www.playitagainsportstempe.com/', 'https://www.titlemax.com/store/las-vegas-nv-16-fort-apache-title-loans/?utm_source=yelp&utm_medium=listing&utm_campaign=places&tmx_id=771c0159ac754cf&sf_traffic=paid_listing_yelp', None, 'http://www.twosmallmen.com/ontario-movers/toronto-movers', None, 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1212', 'https://www.gastonvet.com', None, None, 'http://www.foodlion.com', 'http://www.fairmont.com/pittsburgh/?genid=yelp_pgh_yelp_basic&utm_source=yelp&utm_medium=paid_referrer&utm_content=pgh&utm_campaign=yelp_basic', None, None, None, 'https://www.regions.com/Locator/Branch/bank-branch-Champaign-Il-Champaign', 'http://www.flowersbyLingky.com', None, 'http://www.petersonac.com', None, None, None, 'http://www.aestheticsbydeena.com', None, None, 'http://www.indiandelhipalace.com/', None, 'https://www.salstattooandbarbershop.com', 'https://lvcollege.net', None, None, None, None, 'http://www.charlottegrillco.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', None, None, 'http://www.thevaperylv.com', None, None, 'https://www.sewickleyymca.org', None, 'https://www.hokaido-sushi.com', None, None, None, None, None, None, 'http://www.puccisalon.com', 'http://storelocator.staples.ca/stores/en_CA/ON/Newmarket/57', 'http://www.a1sewer.com', 'https://www.bestmortgagebrokerlasvegas.com', 'http://www.oakparkpethospital.com/index.html', None, 'http://www.biaofscottsdale.com', None, 'http://www.polishfestival.ca', None, 'https://thehomemortgagepro.com', '1592286786', None, None, 'http://www.oakmontdeli.com', None, None, 'http://www.juliosbarrio.com', 'https://www.holyangelsnc.org/cotton-candy-factory', 'http://strayer.edu', None, None, 'http://www.nbarizona.com', None, 'http://www.greenspeedexpress.com', 'http://www.niceonenails.com', 'http://www.lfoptical.com', None, '1592286810', None, 'https://lachilaca.com', 'http://www.lnsportspark.com', '1592286817', 'https://allthingsforu.com', None, 'http://www.emzysalon.com/', None, 'http://www.irontaloncrossfit.com', 'https://www.guidedtoronto.com', None, None, 'http://www.alphaecological.com/locations/pest-control-arizona/', None, None, None, None, None, 'http://www.alignlv.com', None, None, None, 'http://hannyspa.com', None, None, None, '1592286843', 'http://www.raeimages.com', None, 'https://www.menswearhouse.com/store-locator/4406?utm_source=yelp&utm_medium=listing&utm_content=4406&utm_campaign=OH', 'http://autoboyzservicecenter.ca', None, 'http://www.harbourfrontcentre.com/venues/natrelrink/', 'http://www.davesmarkets.com/', None, None, 'https://www.visioncenterslv.com/summerlin/', None, 'http://www.asyouwishpottery.com', 'http://www.raisingcanes.com/location/arizona/scottsdale/great-scott', 'http://www.drsglosik.com', 'http://www.hendersonvapor.com', None, None, None, None, None, 'https://eltacazo.com', 'https://www.choicehotels.com/wisconsin/madison/econo-lodge-hotels/wi413/rates', None, 'http://www.tigeryakitori.com', 'http://mopify.com', 'http://www.starslocker.com', None, 'http://www.springmountaintreatmentcenter.com', 'https://deals.homejoy.com/exclusive?s=US_YEL_YEL&utm_source=US_YEL&utm_medium=YEL&utm_campaign=US_YEL_YEL_WSL_LO-PHX+Phoenix', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://sudforno.com', 'http://www.madelinesbtq.com', 'https://www.ncsecu.org', 'https://www.absolutedental.com/locations/las-vegas/2301-e-lake-mead/', None, None, None, 'http://www.shahimahal.ca', None, 'https://crossfitinfinitestrength.com', 'http://www.goldspike.com', None, 'https://www.walts.com', 'http://www.safeway.ca', 'https://locations.theupsstore.com/az/mesa/2753-e-broadway-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.oldnavy.com/products/las-vegas-nv-store-5811.jsp', None, None, 'http://mtautobodyohio.com', None, None, None, None, 'http://www.fourpointsphoenixnorth.com/spice-restaurant', None, None, None, None, 'http://www.emperor-chinesecuisine.com', 'http://vivopizzapasta.ca', 'http://goubuli.ca', 'http://www.torontohumanesociety.com', None, 'http://www.suncoastcasino.com/entertainment/suncoast-showroom?disid=wmm_yelp_sc_corporate_suncoastshowroom_organiclink', 'http://epiccarrental.com', None, 'http://www.greatclips.com/salons/9261', None, None, None, None, None, 'https://www.novahomeloans.com/las-vegas-office/', '1592286954', 'http://robertostacoshop.com', None, 'https://avedaarts.edu/locations/charlotte/', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/32331+North+Scottsdale+Road-Scottsdale-AZ-85262/storeid=7839?cid=ps_ylp_2020', None, 'http://www.superstore.ca', None, None, '1592286972', 'http://simmonds-plastic-surgery-care.net', None, None, None, 'http://www.npeyes.com', 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', '1592286983', None, 'http://www.timhortons.com', 'http://www.eggsmart.ca', None, 'http://www.academic-urology.com', None, None, None, None, 'http://www.gonesailingadventures.com', None, 'http://www.freepeople.com/', None, None, None, None, 'http://www.dmv.nv.gov', 'https://www.hilton.com/en/hotels/cleshhw-homewood-suites-cleveland-sheffield/?SEO_id=YELP-HW-CLESHHW', 'http://www.lids.com', 'http://www.korean-bbq-restaurant.com', 'http://phoenix.gov/parks', None, 'https://grandeitalianrestaurant.com', 'http://www.frontinopest.com', 'http://www.YogaOnSeven.com', None, 'http://www.vegassprinklers.com', 'http://www.karenskrystalbrittles.com', None, None, None, None, 'http://www.gentlemenchambers.com', 'https://www.pizzahut.ca/store-details/store-R31407/pizza-hut-Scarborough', 'http://www.pejmansalon.com', None, None, None, None, 'http://www.titanmufflers.com', None, 'http://www.certifiedautorepaircenters.com/CertAutoRepair/guest/view/shop.do;jsessionid=C757EE5042715E7DAF8AD192FC9C8C5A.tc-carc?SHOPID=8201', None, None, 'https://www.anytimefitness.com/gyms/2293/Amherst-OH-44001/?utm_source=yelp&utm_medium=local', 'http://www.somethinginthewater.org', None, 'http://Scene75.com', 'http://youniqueantiquesgifts.blogspot.com/', None, None, None, None, None, None, None, 'https://www.wingstop.com/location/wingstop-711-gilbert-az-85297/menu', None, None, 'http://www.lorenzopizzeria.ca', None, None, None, 'http://bluelemon.com', None, None, 'http://www.nextcare.com/locations/az/chandler/?utm_source=Yelp&utm_medium=Local&utm_campaign=chandler', None, None, None, None, 'http://www.homedepot.com/l/Mississauga-Heartland/ON/Mississauga/L5V-3E4/7132', None, None, None, None, None, None, 'https://bostonpizza.com/en/locations/chestermere.html', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, None, 'http://www.stclairgreetings.com', None, 'http://avivaclinic.ca', None, 'http://garyhuntsmanlaw.com', None, 'http://www.ertactical.com', None, 'https://order.qdoba.com', None, 'https://www.lvscc.com/warm-springs', None, None, None, 'https://www.classypetstyling.com', 'http://cornerpubcharlotte.com/', 'http://www.guarinoscleveland.com/', None, None, 'http://www.stanhywet.org/', None, 'http://nvnailspanc.com', 'http://www1.shoppersdrugmart.ca/en/store-locator/store/774', 'http://www.pghgreenclean.com/', None, None, 'http://www.azfvc.com', 'http://uniqueautotinting.com', 'https://highlandspringshealth.com', None, None, 'http://www.garciasmexicanrestaurants.net/', 'http://brimbrewery.com', 'https://nevadatitleandpaydayloansinc.com/locations/NV0340/las-vegas/las-vegas/1298-north-nellis-blvd', 'https://www1.shoppersdrugmart.ca', 'http://www.badgerlandmls.com', 'http://www.janieandjack.com', 'http://www.shoneys.com', 'http://www.smilesbyharris.com', None, 'https://www.ilsos.gov/facilityfinder/facilityfinder?facilityId=135&command=getFacilityDetails', None, 'https://patients.scnm.edu', 'http://www.ncsummer.utoronto.ca/', None, None, 'http://www.mygalsal.com', None, None, 'http://lvnmedicalmassage.com', 'http://www.colonial-management.com', None, 'http://ffb.com', 'http://bunchoffunplayland.com', 'http://www.structube.com', None, 'http://www.altonlane.com/yelp#/?utm_source=yelp&utm_campaign=yelp-homepage_CHO&utm_medium=organic', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=2692', 'http://subway.com/', None, None, 'https://www.delta.com', 'http://www.elfumador.com', None, 'http://www.katrinawallace.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/17120+Chagrin+Blvd-Shaker+Heights-OH-44120/storeid=3346?cid=ps_ylp_2020', None, None, 'http://www.midas.com/madison/store.aspx?shopnum=2181&dmanum=532001', None, 'http://www.alpsautorepair.ca/', None, None, 'http://www.footlocker.com', 'http://www.northendwinefoodfun.com', 'http://www.versagrafix.com', None, None, None, 'http://www.challengefinancialservices.com', 'http://www.thedandelionyyc.ca', 'http://originalgrooming.com', 'http://www.parisnailslv.com', None, None, '1592287215', None, None, None, 'http://www.framboisebakery.ca', 'https://www.stpiobakery.com', None, None, 'http://www.discounttire.com', None, 'http://marksbolts.com/', None, None, None, 'http://www.timhortons.com/ca/fr/locations/get-directions.php?utm_term=QC&utm_campaign=Local_Search&utm_content=Lasalle&utm_source=Google&utm_medium=Local&id=101439', 'http://inapickleparrots.com', None, None, None, None, 'http://www.StMarysChapelCharlotte.com', None, 'http://www.aallriteflooring.com', None, None, None, None, 'http://www.wesdschools.org', 'https://www.supercuts.com/locations/pa/bethel-park/south-hills-village-haircuts-8899.html', None, None, 'http://www.newlinemotors.net', 'http://www.cainortho.com', 'http://www.bikeemporium.com/', None, 'http://www.crystalcreekapts.com', None, 'http://www.indocanadasalonandspa.com', 'https://www.dvsmiles.com/Avondale-Dentist/1237/l', None, None, 'http://www.fellinislv.com', 'https://rines-rims-michoacan.business.site', 'https://www.usps.com/', 'http://www.crycool.com', 'http://www.torontomufflerandbrake.ca', 'https://www.crustrestaurants.com/the-ostrich', None, 'http://www.smilesonbell.com/', None, 'https://www.hardees.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://bartelsbusackpethospital.com/', None, None, 'http://www.tlcroofservices.net', 'http://www.davescarcareaz.com', None, None, '1592287304', 'http://www.curtissteel.com', 'http://soupersalad.com/', 'http://www.chaska.com', None, 'http://www.beltlinedentalcare.ca', None, 'http://www.casadeluzlasvegas.org', None, None, 'http://imajschool.org', 'http://www.coffeeculturecafe.com', '1592287322', 'http://trendingstylespgh.com', 'http://www.steviespizza59.com', None, 'http://www.maac.com/north-carolina/charlotte/post-south-end?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', None, None, 'http://www.theinvestorhub.com/', '1592287338', None, None, 'https://www.nationalcar.com', None, None, None, 'http://www.indiamix.biz', '1592287346', None, 'http://crushertermite.com/', 'http://www.applebees.com', 'http://www.sammyspizza.com/location/las-vegas-flamingo', 'https://www.effortlessinsurance.com', None, 'http://www.livyogastudio.com/', 'http://www.tandyleatherfactory.com', None, 'https://www.anytimefitness.com/gyms/3864/Cheswick-PA-15024/?utm_source=yelp&utm_medium=local', None, None, 'http://www.JohnnyLegends.com', 'http://www.mrgreek.com', 'http://www.super8.com', None, 'http://www.premierpatioaz.com', None, '1592287377', 'https://store.vioc.com/nh/concord/232-loudon-rd-03301-AB0020', 'https://www.clevelandaxethrowing.com/?utm_source=yelp&utm_medium=websiteclick', None, 'http://www.fgbradleys.com', None, None, 'http://www.yetinailsnspa.com', None, 'http://www.dynocomp.com', 'http://www.esicleveland.com', 'http://www.bistrofive61.com', None, 'https://www.bannerhealth.com/locations/gilbert/banner-health-clinic', 'http://www.reskin.pro', 'http://absolutedentalaz.com/', 'http://heartcenteraz.com/locations/central-phoenix-office', 'https://centerforsightlv.com', None, None, None, 'http://www.puffersfloral.com', '1592287417', None, None, None, None, 'https://www.officedepot.com/storelocator/nv/north-las-vegas/office-depot-2143/', None, 'http://markhamsubaru.com', 'http://www.portraitinnovations.com', None, 'http://www.mahalosalons.com', 'https://www.bannerhealth.com/locations/gilbert/banner-health-clinic-2', None, 'http://www.ebenezerhairbraiding.com', 'http://www.osmaz.com', None, 'http://www.imprintpilates.com', 'https://www.irsvegas.com', 'http://progunclub.com/', 'https://www.meineke.com/locations/pa/pittsburgh-1109/?utm_source=yelp&utm_medium=xvc', 'http://khoosgarden.com', None, None, None, 'http://www.sundialaz.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.newtoyouupscaleresale.com', 'http://www.chefsdoor.ca/', 'http://www.frglv.com/#/mike-moreys-sipntip', 'https://lookoutaz.com', 'http://www.paperstudio.com/', 'http://www.lickshomeburgers.com', None, None, None, None, 'http://www.audibedford.com/', 'http://www.parspersiancuisine.com/', None, None, None, 'http://www.headwino.com', None, 'http://grapeableswinebar.com', 'http://www.peoriadentalcenter.com', None, None, 'http://campusbiryani.com', None, 'http://drefamilydental.com', None, 'http://www.cullimorefamilydentistry.com', 'https://www.theblackcatcoffee.com', 'http://www.the-alley.ca', 'https://www.vitalant.org/Locations2/Pennsylvania-Pittsburgh/North-Hills-Donation-Center.aspx', None, 'http://www.tailwaggersddc.com/index.cgi?page=home&location=verona', None, None, None, None, None, None, 'http://www.chalkerspub.ca', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.caseysgrillbar.com/', 'https://alleyfitnesslv.com', None, None, None, 'http://www.the-alley.ca', None, 'http://www.soccerzonevegas.com', None, None, None, None, 'http://paintproslv.com', 'https://www.fastsigns.com/357-chandler-az', None, 'http://www.maidperfectlyaz.com', 'http://www.lazarou.vegas', None, None, 'http://www.NapolitanosItalianMarket.com', 'http://www.kidtastics.com/', 'https://saramosleydds.com', 'http://alterationworld.net', 'https://www.zoup.com', None, None, None, 'http://cienmotorwerks.com', 'https://www3.hilton.com/en/hotels/nevada/hilton-grand-vacations-at-the-flamingo-LASFLGV/index.html?SEO_id=YELP-GV-LASFLGV', 'http://www.fitnessbattalion.net', None, 'https://www.take5oilchange.com/locations/oh/cuyahoga-falls-152/', 'http://jared.com', None, 'http://www.hobbytown.com', 'http://www.sunsetfence.com', 'http://www.theirishgifthouse.com/', 'http://www.citysightseeingtoronto.com', 'http://www.legendssportsbarmadison.com/', 'http://www.floririvillage.com', 'https://www.wyndhamhotels.com/hotel/11415?tel=18007606483&iata=00093785&cid=fe:tl:20170523:yl:pp:tlus:11415', None, None, None, None, 'http://aworthydogg.com', 'http://www.northscottsdaledental.com/', 'http://www.harrahs.com/casinos/caesars-palace/casino-misc/caesars-palace-nightlife-detail.html', None, 'http://www.collegeplanningnet.com', None, 'http://www.acmoore.com', None, 'http://atikastyles.com/', 'http://www.mckibbinsirishpub.com/pointeclaire.asp', None, 'http://www.riversedgetactical.net', 'http://www.karmatattooaz.com/', None, 'http://www.bellapatio.net', None, 'http://www.traditionaltastebakery.ca', 'http://www.cvs.com/minuteclinic', None, None, None, None, 'http://vanitybodysculpting.com', 'http://www.optimasonoranvillage.com', 'http://thelandmarksmile.com/matthews/', 'http://azmobileglass.com/', 'http://www.eastvalleyauctions.com/', None, 'https://locations.wendys.com/canada/on/markham/9970-highway-48', None, 'http://www.burlingtoncoatfactory.com', None, None, 'http://www.xanaducoffee.com', None, 'http://www.quality1stglass.com', 'http://www.bowlofheaven.com', None, None, None, None, 'http://www.lvangelcare.com', 'https://www.oldetownelaundry.com', 'http://www.filenesbasement.com', None, 'http://www.saleyla.com', 'http://tattoosbydannyfrost.com', 'http://www.oasisemeraldvegas.com', 'http://www.sochuhouse.com/', None, 'http://l.macys.com/fashion-show-in-las-vegas-nv?cm_mmc=Yelp_Stores-_-LasVegas-_-n-_-532&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Las+Vegas_532&m_ac=yelp_stores&m_ag=n', None, 'http://www.fspt.guru', None, 'http://www.lotusclubfightandfitness.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.precisiondentallv.com/', None, None, 'https://beautyshoppe.co/locations/seymour-building/', None, '1592287685', 'https://www1.shoppersdrugmart.ca', 'http://greencrosscenter.com', None, 'http://www.woodenstonegallery.com', '1592287693', 'https://www.chpt2restaurant.com', 'http://www.starbucks.com/store/9937/', 'http://www.villasouthside.com', 'http://www.fabriziosalonoh.com', 'http://www.epicsalonaz.com', 'https://arizona.weidner.com/apartments/az/phoenix/bolero-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://premiermotorcarsnv.com', None, None, None, 'http://www.hereortherenotary.com', None, None, 'http://www.glasshouseaz.com', 'http://www.cefalospgh.com', None, 'http://www.ridgeoncharleston.com', None, None, 'http://www.ambrosiacalgary.com', 'http://www.sherwin-williams.com/store-locator/paint-store/Surprise/AZ/8268', None, 'http://www.cwsoa.com', None, 'https://www.barreyna.com', 'http://www.netprintship.com', None, None, 'https://www.walmart.com/store/1380/las-vegas-nm/details', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://tamarindexpress.business.site', None, None, None, 'http://www.idealcoffee.ca', 'http://www.mbarn.com', 'http://nailfetishnv.com', 'http://NARepair.com', 'https://www.goprodoorandglass.com', None, None, None, 'http://www.sunburstpm.com', 'https://www.chick-fil-a.com/raintreedriveat101', 'http://www.driveclassic.com', 'http://www.kfc.com', None, None, None, 'https://jonsmithsubs.com/locations/las-vegas-grand-flamingo-center-nv/?utm_campaign=Yelp_CPC&client=7019-80005&utm_medium=Local_Review_Sites&campid=20&utm_source=yelp', 'http://opticalexpressionsaz.com', None, None, 'http://www.mesabarberschool.com/', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', '1592287780', None, 'http://www.horizonanimalhospital.com', 'http://www.arizonaterritorialadventures.com', None, 'https://gomalleys.com', 'http://www.stahlskentbakery.com/', None, None, None, None, 'http://www.charlottepetsitting.com/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', None, None, None, 'https://legacy-urgent-care.business.site', None, 'http://www.angelospizzeria.us', None, 'http://www.mumuso.com/en', 'http://www.blacks.ca', 'http://www.marbleslab.com/', None, None, None, 'http://alfawal.ca', 'http://www.arizonagranitepro.com', 'https://www.patspizzaplus.net', None, 'https://www.rmcf.com/NC/Charlotte50682', 'http://www.theblackroomvegas.com', None, None, 'http://www.fantasticsams.com', None, None, None, None, 'http://www.carolinashealthcare.org', 'http://www.myfitnesslv.com', None, 'https://pabellonpgh.com', None, 'http://lostourhome.org', 'http://www.charlotteirrigation.com', None, 'http://www.thebutcherblocklv.com', 'https://fleetsfood.com', 'https://stores.petco.com/nc/huntersville/pet-supplies-huntersville-nc-2769.html', 'http://yogatherapytoronto.com/', None, 'http://www.damangione.com', None, None, 'https://www.ecoshieldpest.com/landers/general-pest-control/?utm_campaign=organic&utm_medium=website&location=6682&utm_source=yelp', None, 'http://www.kellywarnerlaw.com', None, 'https://locations.rallys.com/oh/cleveland/1481-west-117th-street/?utm_source=Yelp', None, None, None, None, None, None, None, 'https://www.davesmarkets.com', None, 'http://www.zales.com', 'http://www.rmrcc.com', None, None, 'http://www.marbilnursery.com', 'http://www.theislandscaribbean.com/', None, None, 'https://www.cubesmart.com/colorado-self-storage/lakewood-self-storage/208.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', None, None, None, 'http://www.yongestclairoralsurgery.com', 'http://www.truerunner.com', None, None, None, 'http://www.phobinhminhcalgary.com', None, 'https://www.hilton.com/en/hotels/cltathx-hampton-suites-charlotte-airport/?SEO_id=YELP-HP-CLTATHX', None, 'http://www.winkydesigns.com', None, None, None, 'http://www.kintonramen.com', None, 'http://www.michaelangelosfoods.com', 'http://www.jkchinesegourmet.com/', None, None, None, None, None, 'https://www.gorefreshdental.com/locations/refresh-dental-willoughby-hills/', None, 'http://www.splatcakesnsuch.com/', 'https://campbellssweets.com', None, None, 'https://locations.panerabread.com/pa/ross-township/7217-mcknight-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', None, 'http://www.rpmse.com', 'http://www.ultimateconsignment.com/', None, 'http://www.gioninos.com', None, 'http://www.justcleanwindows.ca', 'https://order.whichwich.com/menu/which-wich-birkdale-village', 'http://www.nomnomsyogurt.com/', None, 'https://www.valentoursrestaurant.com', None, 'http://beautycollection.ca', 'http://www.milestonesrestaurants.com/', 'http://pallottaspastries.net', 'http://furnitureplusinc.com/', 'http://www.stjoanofarc.com/', 'http://www.prettycutanddry.com', None, 'https://www.aldoshoes.com', 'http://www.riosalado.edu/cafe', 'http://www.conns.com/store-locator/arizona/chandler-85224', 'http://www.phoenixpubliclibrary.org/Locations/Pages/Desert-Sage.aspx', None, None, 'http://www.ArcadiaPediatricDental.com', 'http://www.affordableslotmachinerepair.com', 'http://www.nvfirm.com', 'http://www.durandbridal.com', None, 'http://www.lpautobody.com/', None, None, None, 'http://www.socuteboutique.com', None, 'http://www.pizzabrutta.com', None, 'http://www.masterofwoodfloors.com', 'http://www.lonetreegolf18.com', 'http://www.mazzulos.com', None, 'http://ciderhouseroncy.com', 'http://www.lasvegascolonhydrotherapy.com', None, 'http://www.royalefinediningbanquet.com', None, None, 'https://www.metro.ca/en/find-a-grocery/329', None, None, None, 'http://jpautolv.com', 'http://www.petitnuage.ca/', 'https://www.hilton.com/en/hotels/phxtuhw-homewood-suites-phoenix-tempe-asu-area/?SEO_id=YELP-HW-PHXTUHW', 'http://www.ppcp.org', 'http://www.the47to.com', None, None, None, 'http://www.lazeezshawarma.com', None, None, 'http://www.DozenBakeShop.com', None, None, None, 'http://www.stmatthewsbbq.ca', 'http://www.scdrealty.com', 'http://www.toptiercakescleveland.com', None, 'http://www.robertsroofandfloor.com', None, None, 'http://nevadafoot.com', 'https://www.germainemarine.com', 'http://champaign.redwingshoestore.com', 'http://www.vaporcloudlv.com', None, None, 'http://www.middletontaxservices.com', 'https://locations.smoothieking.com', None, None, None, 'http://barefootnailbar.com', None, 'http://www.artesiakb.com/', 'http://www.setmefree.ca', None, None, None, None, None, None, 'http://www.urbanyogaphx.com', 'http://www.abviphoenix.com/', None, 'http://hairlogix-asu.com', None, 'https://locations.vitaminshoppe.com/az/surprise/vitamins-supplements-surprise-az-597.html', None, None, None, 'http://www.uscellular.com', 'http://www.superstarcarwashaz.com/fullservice.php', None, None, 'http://www.ledelicepastryshop.com', 'http://www.jcautobodyinc.com/', 'http://thedonutshoppephx.business.site', None, 'http://www.pulmonarylasvegas.com/', 'http://affderm.com', None, None, 'https://www.salonafton.com/', '1592288129', None, 'http://discountmobilepetgrooming.com', 'http://www.beyermotorworks.com', 'http://www.haochee.com', 'http://www.atembis.com', None, None, None, None, 'http://www.preciouspawspetsitting.biz', None, None, 'http://www.sarouja-rx.com', 'http://dentalofficecharlotte.com', None, None, 'http://www.superior-tire.com', 'http://northsideanimal.vet', 'http://www.reviewjournal.com', 'http://6studio.ca', None, None, None, 'http://locations.michaels.com/az/mesa/2778/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.diamonddeli.us/', 'http://shoppesatparmaoh.com', '1592288167', 'http://restock23.com', 'http://www.onecoffeecoaz.com', 'http://www.sarastotalspa.com', 'https://www.forever21.com', None, None, None, None, 'http://radioshack.com', 'https://dukout.com', 'https://www.superflytoronto.com', 'http://www.findlaycadillac.com', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___biltmore', None, 'https://www.carcosmeticsglass.com', 'http://www.zhengtravel.com/visa-eng', 'http://www.phsurgery.com', 'http://www.coachingbywendy.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, 'http://www.saigonrex.ca', None, None, 'http://sunglassopticstudio.com', 'http://www.flipconsignment.com', 'https://www.tileshop.com/store-locator/madison.do', None, 'http://www.2000days.net', 'http://happywokmadison.com/', 'http://www.lakespinespecialists.com', 'http://www.jennipho.com', 'http://www.brunswickfamilydental.com', 'http://www.ginospizza.ca', 'http://www.spiritexpeditions.com', 'http://www.muzikclubs.com', None, 'https://www.rosatispizza.com/location/ocotillo-az/', 'http://www.sallybeauty.com', 'http://www.famousfootwear.com/?partnerid=YELP', 'http://www.rossstores.com', 'http://www.petvalu.com', 'https://www.mensvitalitycenter.com', 'http://pointe-ui.com/', 'http://www.billiardsnmore.com', None, 'https://azpoolandoutdoor.com', None, 'https://www.allegiantair.com', 'http://www.ohanakenpokarate.com', 'http://www.suncitydrycleaners.com', None, None, None, None, None, None, None, None, None, 'http://www.bajasandblasting.com/', 'http://www.zara.com', 'http://bcpest.net', None, 'http://unionvilleac.com', None, 'http://www.croquescottsdale.com', None, None, 'http://www.mesaobandgyn.com', 'https://www.torontopearson.com/Components/Templates/Retailer.aspx?RetailerID=21474841383', 'https://www.redlobster.com/locations/list/az/scottsdale/4802-e-cactus-road', None, 'http://www.fivestardentistrypittsburgh.com', None, 'http://www.phoenixflowershops.com', 'http://www.powerhousegym.com', None, 'http://buildingtrustplumbing.com', None, None, None, 'http://www.wildwesthorsebackadventures.com', None, 'http://nimbuswatersystems.com/', None, 'http://carolinahomes4sale.com/', 'http://www.ranchovistaapts.com', 'https://www.circlek.com/store-locator/us/avondale/3-e-main-st/2700822', None, None, 'http://www.estrellawomenshealthcenter.com/home/locations.php', 'http://www.merontogo.com', None, 'http://www.GlobeCafeLV.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357456&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'https://bostonpizza.com/en', 'http://www.tempefestivalofthearts.com', 'http://www.vegasprofessionalaudio.com/', None, 'http://www.irisdbridal.com', 'https://www.statefarm.com/agent/US/AZ/Scottsdale/Dan-Vukovic-BM36P3MY000?cmpid=K2V4_BLM_0006', 'https://www.hertz.com/rentacar/location/unitedstates/northcarolina/charlotte/CLTT12', 'http://www.interiorstoinspire.com', 'http://www.chinachefavonlake.com', 'http://www.hcpnv.com', None, 'http://www.myvisioncare.com', None, 'http://www.poolandspahub.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'https://artinnatrunway.wixsite.com/home', None, 'https://stores.bedbathandbeyond.com/North%20Olmsted-OH-44070-458', None, 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', 'https://dannys-glass-repair.business.site', None, 'http://www.dsldogtraining.com', 'https://www.chandlermoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, None, None, 'http://kiintoronto.com', None, 'http://www.crossroadsfarm.com/', 'http://www.wetstyle.ca', '1592288371', None, None, None, None, 'http://www.ccfpd.org', 'https://www.donnakaran.com/store-locator/dkny+las+vegas.do', 'http://www.lsmchiro.com/contact/locations/dean-st-marys-madison', None, 'https://mtt.tickettransaction.com', 'http://www.barkinghampalacehenderson.com', 'http://noahsarkblc.org', '1592288390', None, None, None, 'http://www.elyriahyundai.com', 'http://www.greatclips.com/', 'http://www.amishgaragebuilders.com', None, None, None, '1592288401', 'http://wagnershoes.com', None, 'http://www.mcgardensfloristandgifts.com', 'http://theabbot.ca', 'http://www3.ttc.ca/Routes/511/Northbound.jsp', None, None, None, None, 'http://www.fusionsushithai.ca', None, None, 'http://oscars.ca', 'http://www.dellangelhall.com/', None, 'http://www.ganleyfordwest.com', 'http://www.hennabypurvi.com', 'http://monaghans.ca', None, 'http://www.nvclimbing.com', 'http://candynailsspa.com', None, None, None, 'http://www.caffeartigiano.com', 'https://www.1298sushi.ca', 'http://www.galleryrussia.com', 'https://www.tempoapts.com', None, 'http://ajbuilders.com/', None, None, None, 'http://www.restaurantdandylion.com', 'http://www.910liveaz.com', 'http://www.tiptopnailsaz.com', None, None, 'https://www.clubpilates.com/broadviewheights/', None, 'http://www.exoticmeatmarket.net', None, None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://p2lawyers.com', 'https://www.apexcustoms.com', None, None, None, None, None, None, 'https://www.spirit.com', None, 'http://ahcfacilities.com/', None, None, None, None, 'http://www.conterestaurantgroup.com/', 'http://lasvegas.jiffylube.com/Locations/Store/1975/4531-N-RANCHO-RD-LAS-VEGAS-NV-89130-3403', None, 'http://www.itali.co', None, 'http://www.edohairbraiding.com', 'http://www.sashimiisland.com/', 'http://prettypleasefashion.com/', 'http://www.alkaramsweets.com', None, 'http://www.threadedbeauty.co', None, 'http://www.metroford.ca', None, 'http://salonfaith.com/', None, None, 'http://www.detoursamericanwest.com', None, None, None, None, 'https://www.lifestorage.com/storage-units/arizona/phoenix/85255/787-near-pinnacle-peak/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-787&utm_content=website-link&howheard=IYE', 'https://www.snakesandlattes.com', 'http://www.tykesntotsindoorplay.com', None, 'http://bistropicbois.com/', None, None, None, 'http://www.crateandbarrel.ca', None, 'http://www.scottenglishphoto.com', None, 'https://abcglasspgh1.com', 'http://www.timhortons.com/', None, 'http://sinusreliefcenter.com', 'http://www.canampm.com/papago-gardens', 'http://www.casamelspizza.com', 'http://www.247techies.com', 'http://maidpro.com/charlotte', None, None, 'http://standardtap.ca', None, 'http://www.happykidsvegas.com', None, None, None, None, None, None, None, None, None, 'https://locators.bankofamerica.com/az/sunlakes/financial-centers-sun-lakes-11194.html', None, None, 'https://www.sweye.com/locations/mesa-stapley/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-mesa-stapley&utm_content=website', None, None, None, 'http://www.allmartialartssuppliesog.com', None, 'http://www.elegantbrows.com', 'http://www.fluffice.com', 'http://imageeyecarenv.com', None, None, 'http://www.goodmansjewelers.com', None, 'http://mjreedjewelers.com', None, None, 'https://www.usps.com/', 'http://mindtwistescapes.com', 'http://www.lecafedulac.com', 'http://www.flagworldandsportsusa.com', None, 'http://mrgreek.com', 'http://www.pghpopcorn.com', 'http://www.jefferysforhair.com', None, 'http://www.riopizza.co', 'http://www.doctorfeldman.com/', None, None, None, 'http://www.sagamorepitstop.com', 'http://boscosbiscuits.com', None, None, 'https://www.thegypsymobileminister.com', 'http://www.geebeauty.com/', None, 'http://www.sewingsupplydepot.com', 'https://locations.wendys.com/united-states/oh/urbana/734-scioto-st.', None, 'https://younglawlive.com', 'http://phxclean.com', None, None, 'http://www.sweetstrawberrycakelv.com', 'http://charlotte.carsandcoffee.info', None, 'http://leosonmain.com', 'http://www.bodyrevolution.net', 'https://katlotus.simplybook.me/v2/', None, None, None, None, 'https://www.pizzahut.ca/store-details/store-R32814/pizza-hut-Mississauga', 'http://www.samjamescoffeebar.com', 'http://www.mammaspizza.com', 'https://eyelashclub.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.youmoveme.com/ca/toronto?utm_campaign=yelp&utm_medium=ubl&utm_source=toronto', None, None, 'http://davenezia.ca', None, None, 'https://www.advancedderm.com/medical-professionals/365/MiriamSBettencourt.aspx', 'http://www.brenckles.com', 'http://www.nadiasalon.com', None, 'http://www.littlerangoon.com', 'http://www.summitmetroparks.org', 'http://www.fye.com', None, None, 'http://www.wedgebar.com', None, None, None, None, None, 'https://www.metro.ca/en/find-a-grocery/312', 'http://www.goldenent.com', None, 'http://trifectagrill.com/', 'http://www.professionalsewandfit.ca', None, 'http://www.thetrunkspace.com', 'http://www.martinautosalesinc.com', None, None, None, None, 'http://www.ballyslasvegas.com/restaurants/tequila-bar-and-grill.html#.U3w1yXKSzDw', 'http://hakkachopsticks.com', 'http://www.gvmontessori.ca', 'http://www.dunkindonuts.com', None, 'http://www.charliesdrainservice.com', 'http://drhorton.com/', None, None, 'http://www.bikramcalgarysouth.com', 'http://www.resetlv.com', 'http://www.blowfishrestaurant.com', 'http://simisterandbranhamdental.com', None, None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://lafromagerie.ca', 'https://www.prometric.com', 'http://www.bistrokent.com/', None, None, 'http://www.mountainviewacademy.ca', None, None, None, None, 'http://www.suavitysalon.net', None, None, None, None, None, None, None, 'http://www.badsassbackdrops.com/', None, 'http://tastyshawarmaandfalafel.food-24h.com', None, None, None, None, 'https://www.shakerwines.com', None, 'http://www.visitingvet.net', 'https://www.epiphanysalons.com', None, None, None, None, None, None, 'https://qrico-mexicanrestaurant.business.site', None, 'http://www.saveonfoods.com/store/seton', 'https://www.speedycash.com/find-a-store/arizona/phoenix/indian-school-and-16th?utm_source=yelpstorelocator&utm_medium=Affiliate&utm_content=afflink', None, 'http://www.dayvolkswagen.com/dealership/about.htm', 'http://www.bellavitarehab.com', 'https://locations.wendys.com/united-states/me/scarborough/205-us-route-1', 'http://www.crossfitpittsburgh.com', None, 'http://orientalfoods.ca/', None, None, 'http://clinicalafamilia.com', None, '1592288805', None, 'http://bluewire.us', 'http://listerpros.com', 'http://www.rickyleesdoghouses.com', 'http://www.bobbetteandbelle.com', None, 'http://BasilicaTattoo.com', None, 'http://www.rollingfusion.com/', None, 'http://souktabule.com', None, None, None, None, 'http://www.katiepenawellness.com', 'http://www.antiquesmadison.com', 'http://www.Montblanc.com', None, None, 'http://espressocafeyyc.com', 'http://www.eatatco.com/location/Charlotte/', None, None, None, None, 'http://www.asapnv.com', None, None, 'https://www.sunrisepreschools.com/locations/baseline-gilbert/?utm_source=yelp&utm_campaign=online_listing_gilbert_280&utm_medium=referral&utm_term=business_url', 'http://www.welldone-catering.com', None, None, 'http://www.bocabargoons.com/scottsdale-az/', None, None, None, 'http://www.tresjachristopher.com?cmpid=f0uo_blm_0006', 'http://www.lowbudgetmovers.net', None, 'http://www.fairplaystores.com', None, 'https://www.amf.com/location/amf-desert-hills-lanes?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'http://Theindiankitchenmentor.com', 'http://jackastors.com/location-map/22/', 'https://www.ssmhealth.com/locations/location-details/davis-duehr-dean-eye-care-madison-regent-street', 'http://www.kellysaggione.com', 'http://www.shell.us', None, 'http://www.landscapedesign-az.com', 'http://www.chevys.com', '1592288884', None, 'http://www.gianteagle.com/', None, None, None, '1592288895', None, None, None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.interiorharmony.ca', None, 'http://www.rentaslingshotlv.com', 'http://www.metrofitnessclub.com', 'http://www.ilfornello.com', 'http://www.gofortea.ca/', None, None, 'http://www.rockstarsnowcones.com/', 'http://www.shoedeptencore.com', 'http://www.quiktrip.com', None, 'http://sunstopliquor.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, 'https://www.jerseymikes.com/3137', 'https://www.activegreenross.com/tire-centre/ajax/7-1-westney-rd-ajax?postcode=l1t1p4', 'https://www.fido.ca/consumer/storelocator?store=7861', None, None, 'http://www.woodstoneeatery.ca', None, None, None, 'http://www.7-eleven.com/?yelp=29384', None, None, None, None, 'http://www.movementrestoration.com', 'https://www.hilton.com/en/hotels/phxcthx-hampton-suites-phoenix-downtown/?SEO_id=YELP-HP-PHXCTHX', None, 'https://locations.traderjoes.com/oh/westlake/677/', None, None, None, 'http://spiritandspark.com', 'http://rajmahalrivesud.com', 'http://www.mabelsbakery.ca/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.bankofamerica.com', None, None, None, None, None, 'http://theexchange.com', 'https://www.navyfederal.org/?cmpid=bn%7Cyelp%7Cevgrn%7Cbrn%7Cnull%7Cnull%7C01/13/2020%7Cml%7Cnull', None, 'http://www.deltaairllc.com', 'http://bowestappliances.ca', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'https://thepetclub.net', None, 'http://www.everestmedicalgroup.com', 'http://www.toronto.ca/path', '1592288991', None, None, None, None, 'https://www.lablissllc.org', None, None, 'http://www.dogearedpagesusedbooks.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://badaxethrowing.com/axe-throwing-toronto/', 'http://www.robbiessmokehouse.com', None, 'http://www.aquavetsaz.com', None, None, 'http://www.everest.edu/?dmredirect=YPINSMTP&date=3', 'http://www.pilatesbytracy.com', None, None, 'http://www.desertpaininstitute.com/', 'http://www.flamingolasvegas.com/restaurants/club-cappuccino.html#.UuGYloXTm_U', '1592289032', 'http://www.planetsun.ca', 'http://www.yummytummy.ca', 'http://www.omegafcu.com', 'http://www.agaveapt.com', None, None, None, 'http://www.northhillslockandsafe.com', 'http://tokyooneexpress.com', None, 'http://www.avivacentre.com/', 'http://gwrdistilling.com', 'http://www.greatclips.com/', 'http://www.redrockco.com/soma-half-and-quarterman-triathlon', None, None, 'http://grouchos.com/locations/grouchos-deli-of-indian-land-fort-mill', None, None, None, None, None, 'http://www.woltzwindford.com/', None, 'http://www.12thavenuedental.com/', 'http://tea2go.us', None, None, 'http://www.longjohnsilvers.com/', None, None, None, 'https://www.thecorescottsdale.com/the-core-scottsdale-scottsdale-arizona/', None, None, None, None, 'https://www.hilton.com/en/hotels/cltpkhw-homewood-suites-charlotte-north-univ-research-park/?SEO_id=YELP-HW-CLTPKHW', 'http://www.sixtyseven.ca', 'http://whatabakery.com', None, None, None, None, None, None, None, 'http://dagu-usa.com', 'http://www.alteredtails.org', 'http://www.leahlasvegas.com', 'https://www.sevenoakscafe.com', None, None, None, None, None, None, None, 'http://www.lsuc.on.ca/osgoode-hall', 'https://www.gamestop.com/store/us/nv/henderson/2627/pecos-windmill-plaza-gamestop', None, 'https://thebellajadecollection.com', 'http://www.ccpk.info', 'http://www.sky-hvac.com', None, None, None, None, None, 'http://www.webergrillacademy.ca', 'http://www.kristiisaisrealtor.com', 'http://www.todaysmusiclv.com', 'https://www.simmonsfootandankle.com', None, None, None, 'https://www.navyfederal.org/?cmpid=bn%7Cyelp%7Cevgrn%7Cbrn%7Cnull%7Cnull%7C01/13/2020%7Cml%7Cnull', None, 'http://www.gamenightz.com', None, None, None, 'http://www.stampeders.com/', None, 'https://www.crateandbarrel.com/Stores/ross-park-mall/str656', None, None, None, None, None, 'http://hookupmuaythai.com', 'http://www.worldoftile.net/wordpress', 'http://www.muchoburrito.com', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.fremontcasino.com/vegas-hotel-reservations?disid=wmm_yelp_fr_corporate_fremontcasino_organiclink', 'http://www.thecauseyeffect.com', 'http://www.hongkongwokhilldale.com', None, 'http://www.beccaris.com', 'http://www.onthegocasino.com/', 'http://www.dignityhealth.org/urgentcare/az', 'http://www.uptownsushi.ca', None, 'http://stores.interstatebatteries.com/Charlotte_NC', 'http://www.sunrisecaribbean.com', '1592289179', None, None, 'http://www.hakkaspice.com', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', None, 'http://www.sightnsteps.ca/', 'http://clickserve.dartsearch.net/link/click?lid=43700044280215909&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, None, 'http://www.cakedesignslv.com', None, 'http://www.mesapt.com', '1592289202', None, 'http://www.lasvegaslimo.com', None, None, None, 'http://camelbackrehab.com', None, 'http://chicken-now.com/locations.html', 'http://libertyperformancetraining.com', 'http://www.imbibetours.com', None, None, None, None, 'http://www.hometeamaz.com', None, None, None, None, 'https://www.soundrelief.com/location/scottsdale-arizona-hearing-aids/', None, None, 'https://www.zippssportsgrills.com', None, 'https://www.marriott.com/hotel-restaurants/phxdr-jw-marriott-phoenix-desert-ridge-resort-and-spa/twenty6/5543176/home-page.mi', 'http://www.wildwoodclinic.com', 'http://Ginas-Online.com', None, 'http://www.blucigs.com/privacy-policy/', None, None, 'http://www.rapidacs.com', None, None, 'http://www.especiallyselective.com', 'https://www.battlebornac.com', 'https://newimagepaintandbody.com', '1592289257', None, '1592289259', 'http://www.photosbyim.com', 'http://lvmpd.com/', '1592289265', 'http://www.elegantchinesecuisine.com', None, 'http://www.pomegranatecafe.com/', None, 'http://notabenerestaurant.com', 'https://www.ultracollision.com', None, None, 'http://azaiclub.org/', 'http://www.mrleno.com', 'http://www.funslidespark.com', 'http://www.whitakerdentalcare.com', None, 'http://www.phoenixsedationdentist.com/', 'http://www.lasercreationsaz.com', None, 'http://www.catherines.com', 'http://puttersvegas.com', 'http://www.hightain.com', 'http://www.ihop.com', 'http://www.dovecleaners.com', None, 'http://www.pizzanova.com', 'http://www.orfuswrapandgrill.ca/', None, 'https://www.gowireless.com/stores/az/phoenix/phoenix-ahwatukee-foothills/', None, None, None, 'http://www.activelearningprograms.com', 'http://www.skylandfamilyrestaurant.com/', None, 'http://www.vinotecawinery.ca/', None, None, 'http://www.gavinospizza.com', 'http://www.viendong.ca', None, None, None, 'http://www.godspeedmotors.com', None, None, None, None, None, None, None, 'http://www.milliesbakehouse.com', 'http://www.rivierapgh.com/la_riviera_bistro.html', None, 'https://www.culvers.com/restaurants/madison-east-towne', 'http://www.gamestop.com', 'http://steveglasspainting.com', 'http://www.weistaiwanesefoods.com/', 'http://www.buckortwo.com', 'http://www.globalpetfoodstoronto.ca/locations/beaches/', 'https://www.circlek.com/store-locator/us/fort-mill/681-hwy-21-bypass-s/2701507', None, None, 'http://www.theartofshaving.com', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', None, 'http://www.liquidnutrition.com', None, None, 'http://www.redrocklasvegas.com/dining/salt_lick.php', None, 'http://www.perrinechiropractic.com', 'http://stuartposner.md.com/', None, 'https://autotownonline.com', 'https://www1.shoppersdrugmart.ca', None, 'http://massageescapes.com', None, None, 'http://www.binz.ca', 'https://goodwillscwi.org/locations/goodwill-madison-northside/', None, 'http://www.elnewyoricancentralcateringanddelivery.webs.com', 'http://www.tapsiloganusa.com', None, None, None, None, 'http://www.melaindiancuisine.com/', 'http://www.cabridal.com', None, 'http://www.sickkids.ca/', 'https://www.statefarm.com/agent/US/NV/N-las-vegas/Ariel-Rivera-0ZBPT2T0000', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.jlcharlotte.org/?nd=wearhouse', None, 'http://www.fusiali.com', 'http://cactusfootandankle.com', 'http://www.nails90spa.com/', 'http://www.herbal3.com', 'http://www.naturalstitches.com', None, None, None, None, None, None, 'http://www.whitbytires.com', 'http://santaguidafinefoods.com/rapido/', 'https://locations.jackinthebox.com/us/az/cave-creek/29815-n-tatum-blvd', None, 'https://www.lunaireapts.com', None, 'http://www.davischev.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.sharpervisioneyecare.com', None, None, None, 'http://www.fullspectrumbrewingco.com/', None, None, 'http://www.pizzaten.ca/', 'http://www.centurylink.com/', None, None, 'http://www.providenceelectricnc.com/', 'http://www.desertautosaleslv.com', 'http://www.labcorp.com', 'http://www.26acres.com', None, '1592289478', 'http://eyesdts.com', None, None, 'http://www.tuscanylv.com/dining-en.html', '1592289488', None, None, None, 'http://www.poolwerx.com/locations/arizona/pool-shop/riggs-mcqueen-chandler-pool-supplies-services', None, 'http://stratospherehotel.com/Food-Drink/107SkyLounge', 'http://www.myspace.com/belezacommunitycoffee', None, None, 'http://www.allanabraham.com?cmpid=gsdp_blm_0006', 'http://hiltongardeninn3.hilton.com/en/hotels/north-carolina/hilton-garden-inn-charlotte-waverly-CLTCWGI/index.html?SEO_id=YELP-GI-CLTCWGI', None, None, '1592289509', 'https://www.amj-international.com', None, None, None, None, 'http://philsny.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.familyallergyclinic.com', 'http://www.farleysfarms.com', None, 'http://www.thespiceoutlet.com', None, None, None, None, None, 'http://www.zinkamerican.com', None, None, 'http://www.lecorals.com', None, 'http://koala-t-roofing-llc.business.site', 'http://www.cakesbykarin.com', 'http://www.eastyorkpetgroomer.ca', 'https://www.wyndhamhotels.com/hotel/52989?tel=18666154223&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52989', None, None, 'http://www.lettiericafe.com', 'http://www.greenesquarerestaurant.com', None, None, 'https://GLOWSTUDIOPGH.as.me', 'http://www.bigbroncocavecreek.com/', None, 'http://tuttisantiristorante.com/index.php?option=com_content&view=article&id=68&Itemid=465', 'http://www.phonerepaircleveland.com', 'http://www.wildhorsepassresort.com/kai', 'http://www.vegasalon.com/', None, None, 'http://www.redvietcuisine-sushi.com', 'http://www.colonhygieneinstitute.com', None, 'http://www.nathansfamous.com', 'https://www.jerseymikes.com/8032', None, 'http://stores.partycity.com/az/gilbert', None, None, None, 'http://www.aimtopleaselv.com', None, 'http://www.montecarloinns.com/airport-suites/dining.html', None, 'http://www.carpetcleaninghudson.com', 'http://www.littleluxuriesmadison.com', 'http://www.davesfurnitureservice.com', 'https://www.enterprise.com/en/car-rental/locations/us/ct/monroe-24cj.html?mcid=iyp:8368400', None, None, None, 'http://www.talleyspier77.com', 'http://www.cityofmadison.com/parks/find-a-park/park.cfm?id=1241', 'http://www.jpjiujitsu.com', None, 'http://www.fatherandsonpro.com', None, 'http://www.mrthai.ca', None, '1592289620', None, 'http://www.azfinetime.com/', 'http://www.davidottolaw.com', None, 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1386&s_cid=lsl0000001', 'http://www.redtomato.ca', '1592289634', '1592289637', 'https://www.mastercuts.com/locations/wi/madison/mastercuts-east-towne-mall-haircuts-4817.html', None, 'https://elevationspa.net', '1592289646', 'http://www.shawnsfreeapplianceremoval.com/', None, 'https://www.sibbach.com', None, None, 'http://www.OrthoArizona.org', None, None, None, None, None, None, None, 'http://www.stevepowes.com/', 'http://www.joes-sports-bar.com', None, None, 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'http://www.labcorp.com', 'http://www.sirspeedy.com/GlendaleAZ450', None, None, None, None, 'https://www.huntington.com/Community/branch-info?locationId=382', None, None, 'http://www.lussorestaurant.com/', 'http://www.shortstopinsurancenv.com', None, 'https://www.jiffylube.com/locations/nv/north-las-vegas/2042', 'http://www.thepalms.org', None, None, None, None, '1592289688', 'https://union.wisc.edu/dine/find-food-and-drink/harvest-grains', None, 'http://unityoftempe.org', None, 'http://www.pfchangs.com/', None, None, 'http://www.royalliquormerchants.com/', 'http://www.carenamotors.com', '1592289704', None, None, 'http://www.enclaveslv.com', 'http://www.saludjuicery.com/sewickley/', None, None, 'http://www.chuppasmarketplace.com', 'http://www.chefs.edu/Scottsdale', None, None, None, 'http://www.lakeshorecc.ca', 'http://www.foodsystemsunlimited.com/restaurants/asianchao.php', 'https://onestop4flooring.com', None, 'http://www.slabburgers.com', 'https://www.worldgym.com/sheffieldvillage/home', 'http://www.wolfgangpuck.com', None, 'http://www.universalathletic.com/location.php?locid=9', 'http://www.pizzahut.com/', None, None, None, 'http://locations.atipt.com/washington-vegas-nv', 'http://www.gamestop.com', None, 'https://www.hilton.com/en/hotels/pitucgi-hilton-garden-inn-pittsburgh-university-place/?SEO_id=YELP-GI-PITUCGI', 'http://www.themonarchtavern.com', None, 'https://www.thelashloftoh.com', None, None, None, None, 'https://www.sweye.com/locations/sun-city/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-suncity&utm_content=website', 'http://www.kelseys.ca', None, None, None, 'http://www.salonofevidenceuptown.com/', None, 'http://www.studiocycle.ca', None, 'http://nolimitpools.com', '1592289768', None, None, 'http://shopngodeli.com/', 'http://www.lakesidefibers.com', None, None, None, None, 'http://www.backwoodscustomaz.com', '1592289782', None, None, None, 'http://www.therollhouse.com/mentor/', 'http://www.decalmonkey.biz', None, 'http://www.bk.com', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'https://www.tuscanylv.com/restaurant/marilyns-cafe/', None, 'http://www.lasvegasnevada.gov/Find/21108.htm', None, None, 'http://gallaghersaz.com/', 'http://www.headshots.ca/', 'http://www.realtyofnevada.com', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://www.theacetoronto.com/', None, 'http://www.myphoenixhomesearch.com/', 'http://2270keele.webs.com', None, None, None, 'https://www.pizzaville.ca', '1592289822', 'http://www.redmtncollision.com', None, 'http://gilbert.servicefirsthomeloans.com/', None, None, 'http://www.seaportmerchants.ca', 'https://store.vioc.com/oh/north-olmsted/24866-lorain-rd-44070-060026', None, None, 'http://www.timhortons.com/ca/en/locations/locations.php?q_loc=T1X+1V3&q_rad=5', None, 'http://www.manbeastbbq.com', None, None, None, 'https://arizona.weidner.com/apartments/az/phoenix/accolade/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', None, None, 'http://www.harboursportsgrille.com/', None, None, None, None, 'http://premierimagingpgh.com/', 'http://perfectpoolsarizona.com/', 'http://sincityhydrocompany.com/', None, None, 'http://www.bluephies.com/', '1592289864', None, None, 'http://www.landscapecreationslv.com', 'http://www.foodlion.com', None, 'http://pilotflyingj.com/stores/341', 'http://www.stazionecentrale.ca', 'http://www.u-swirl.com', None, 'http://selectbakery.ca/', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.illumelaser.com', 'http://nailsalonscalgary.com', None, None, None, 'http://chadwicks.ca', None, 'http://www.autonationhondachandler.com/', 'http://www.colehaan.com', None, 'http://www.tranzac.org', None, 'http://www.quamsappliance.com', None, 'http://www.paperdestiny.com', 'http://lvgurdwara.com/', None, None, None, None, 'http://www.finderskeepersaz.com', None, 'http://az.tempe.papamurphys.com/pizza_tempe_az_az064.html#fbid=SSeWPjo_eAA', 'http://www.radiantchurch.com', None, 'http://markitmedia.com', None, 'https://www.cranialtech.com/location/az/mesa-clinic_34/', None, 'http://www.mgalaw.com', 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=130&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-130', 'http://xteriousescape.com', None, None, None, 'http://www.opticaldepo.com', 'http://ouellet-lynch.com', 'http://www.gnc.com', 'https://www.signaturestyle.com/locations/ab/calgary/first-choice-haircutters-51196.html', None, None, None, 'http://micamp.com', 'http://hotheadburritos.com/', 'http://www.quiznos.com/', 'http://www.hubeeds.com/', None, 'http://www.maijapaneserestaurant.com/Ayrsley-Town-Location.html', None, 'http://greatlifewellness.ca', None, 'http://apolloconventioncentre.com', None, None, None, None, None, 'http://www.anisecafeaz.com', 'http://adcovegas.com', 'http://www.framarsalon.com', None, 'http://www.thetanco.com', None, 'http://lvradiology.com', 'http://www.romeospizza.com', 'http://www.lanternandscroll.com', None, 'http://www.petco.com', None, 'http://www.subway.ca', None, None, 'http://www.jiffylube.com', None, 'http://www.timhortons.com/', 'https://www.sinfulsweetspgh.com', None, 'http://www.gypsy05.com', None, None, 'http://www.lamophairstudio.com/', 'http://www.fingerprintingpros.net', 'http://animalhospitaloflaveen.com', 'http://www.icyfrosthvac.com', None, None, None, None, None, 'http://www.scouting.org/', None, 'http://www.kibosushi.com', None, 'http://www.theatercenterpittsburgh.com', 'http://www.shoppremier.com', None, None, None, None, None, None, 'https://locations.wendys.com/united-states/oh/amherst/604-north-levitt', 'http://www.westview-heights.com', None, None, None, None, None, 'http://www.heavenlyglowskincare.com/', 'http://katespade.com', 'http://www.allstatecarpet.com', 'http://www.usps.com', None, None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.letsmakeit.ca', None, None, 'http://www.dadscatering.com', None, 'https://christiansfitnessfactory.com/', None, None, 'http://tripletriplepizza.com', 'https://ww.victoriassecret.com/store-locator#/store/1523', 'http://www.jwdover.com/', 'http://www.superiorplusaz.com', 'http://www.spencer4hireroofing.com', 'https://www.budget.com/en/locations/us/nc/charlotte/ib1', 'http://www.boulderdentalgroupnv.net', None, None, 'http://www.azwood.com', 'http://www.roofarizona.com', None, 'http://www.fountainspubandgrill.com', None, 'http://makeoveraz.com', 'http://www.deonsrestaurantco.com', 'http://o-patio-churrasqueira.business.site', None, None, None, None, None, 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB037&Entt=RDMLIB037', None, None, 'http://www.muddypawslv.com', None, None, 'http://www.myperfectbodynow.com', None, 'http://www.sweetjesusicecream.com', 'www.jubileeauditorium.com', 'http://serafina-apts.com/switch_cls%5Bid%5D/34626', 'http://www.hogsandheifers.com/', None, None, 'https://www.talkingstickresort.com/phoenix-scottsdale-concerts-entertainment/degree-270/', None, None, 'http://www.vegasviplimo.com', None, None, None, None, None, 'http://www.originalpancakehousepittsburgh.com', 'http://raisingcanine.ca', None, 'https://www.freshthyme.com', 'http://nailspaindianland.com', None, None, None, None, None, '1592290140', None, None, '1592290145', '1592290147', None, 'http://www.atibalsights.com/', None, None, None, None, None, 'http://www.desertstorage.com/las-vegas-nv-boat-rv-storage', None, 'http://asadamexicanrestaurant.business.site', None, 'https://www.mamaprimozz.com', '1592290165', 'http://www.escapechandler.com', '1592290170', None, 'http://nicksdiner.com/', None, None, None, 'http://chrisschmidtkedds.com/', None, None, 'http://www.halobrewery.com', 'http://pattonstowing.com', 'https://www.sunsetgrill.ca', 'http://WWW.bratchercustompainting.com', 'http://www.sunsetclinic.us', None, 'http://www.big5sportinggoods.com', 'http://hiltongardeninn3.hilton.com/en/hotels/ontario/hilton-garden-inn-toronto-vaughan-YYZVAGI/index.html?SEO_id=YELP-GI-YYZVAGI', None, None, None, 'http://Www.tailracemarina.com', 'http://www.vegastheshow.com', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=38', 'http://www.foodcity.com', 'https://lasvegasliving.com/properties/adiamo/', None, 'http://www.saint22.com', 'http://www.smithapartments-cu.com/', 'http://www.daleouellette.com', 'http://viviry.ca', 'https://www.phoenixmedicalmarijuanacard.com', None, 'https://www.caffeinelakewood.com', 'http://www.rebarlv.com', 'http://masonscreamery.com', 'https://www.courtesychryslerdodgeramsuperstitionsprings.com', 'http://www.scottsdalelaughfactory.com/', None, 'http://www.pizzastudio.com', None, 'http://www.furniturelounge.net', 'http://www.ndkprodj.com', 'http://www.a1vacs.com', None, 'http://www.socialregister.com', 'http://www.repwest.com', 'http://www.swpHomeInspect.com', 'http://www.theriverside.ca/', 'https://www.jinglebarpgh.com', 'http://boosterjuice.com/store-locator', None, 'http://www.dolcelusso.com', 'http://www.simonsushi.com', None, 'http://www.wheelfish.com', 'https://www.cubesmart.com/nevada-self-storage/las-vegas-self-storage/90.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'http://www.peaceofmindhomeinspectionllc.com', 'http://www.thaiexpress.ca/', 'http://bombshellnailandspa.com', None, None, 'http://www.Bellagio.com', 'http://speakofthedevillorain.com', 'http://www.doodledogsboutique.com', 'http://oldnavy.gap.com', None, 'http://www.21stcenturyneurology.com/oldsite/', 'http://www.infinitysend.com', 'http://www.balilaffa.com', 'http://www.achieversmortgage.com', 'http://luganos.com', 'http://www.animalhospitalportcredit.ca/', 'https://www.twistsocialclub.com', 'http://www.bathfitter.com/location/cleveland/', None, 'https://website--4427110145841279093200-nailsalon.business.site', 'http://www.babysfirstimage.com', None, 'http://www.stagedtoselldesign.com', 'https://www.docpopcorn.com/doc-popcorn/location-finder/concord-mills.html', None, 'http://www.libertycyclery.com/', 'http://www.modernpetsalon.com', 'http://www.mustardandrelics.com', 'http://www.garrettflorist.com/', None, 'https://www.jfqlending.com', 'https://thepetclub.net', 'http://www.rent-a-toyota.com', None, 'http://www.buypopculture.com', None, 'http://www.campingworldofmadison.com', 'http://www.tedbaker.com/us/stores/store/70109', 'http://www.hotyogamarkham.com', 'https://blacklinestudios.ca', None, 'http://rubaiyatcalgary.com/', 'http://www.azpremierderm.com', 'http://www.skylinemusic.com', 'http://www.gong-cha.ca', 'http://www.nevadamarblerestoration.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXSF', 'https://www.regmovies.com/theatres/regal-starlight-charlotte/1848?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Starlight+-+Charlotte', 'http://amigoanimalclinic.com/', 'http://www.bigmammasboy.ca', None, 'http://diveworld.ca', None, None, None, 'https://www.usps.com/', 'http://www.elmilagropgh.com', 'http://joeys.ca', None, 'https://www.mccloudacostaclinicalservices.com', 'http://www.lalaserhairremovallv.com', 'http://www.akasmiles.com', None, None, None, 'http://www.elbowsprings.com/', 'http://www.7-eleven.com/?yelp=29384', 'http://coocooscafe.com', 'http://www.hoernigheatingandair.com', None, 'http://www.aaa.com', None, 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.razer.com', 'https://www.bodylogicmd.com/bioidentical-hormone-doctors/north-carolina', 'http://www.thesecretlv.com', 'http://www.anthropologie.com', 'https://agents.farmers.com/nv/las-vegas/rob-rische?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.torshcaters.com', 'http://barewithtaelyr.com', None, 'https://www.target.com/sl/glendale/1806', None, None, 'http://www.laviesouthpark.com', 'https://btssurplus1.asu.edu/spms/public.aspx', 'http://theexchange.com', 'http://www.treeoflifemetaphysical.com', 'http://saikenbar.com', None, 'https://www.firehousesubs.com/locations/nc/gaston-mall', 'https://johnemilyalterations.com', None, None, 'http://www.shopmorninglory.com', None, 'http://www.criminalazlawyer.com', 'http://www.rosenblittdental.com', None, 'http://www.opticalthirty8.com', 'http://www.censeasolutions.ca', None, 'http://www.burritoboyz.ca', 'http://www.runningroom.com', 'https://www.jetspizza.com/stores/ohio/middleburg-heights/7554-pearl-rd?utm_source=Yelp-Ads&utm_medium=Yelp-Ads-SEO&utm_campaign=OH-004&utm_content=Website', 'http://www.pvpzonelv.com/', None, 'http://www.cbdamericanshamanlv.com', 'http://snfac.com/', None, 'http://www.rainbowclubandcasino.com/', None, None, 'http://www.kidtasticdental.com/', 'https://www.walgreens.com/locator/walgreens-9415+w+desert+inn+rd-las+vegas-nv-89117/id=4137', 'http://www.azopt.net', 'http://bfmedaz.com', 'https://www.wyndhamhotels.com/hotel/19261?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:19261', 'http://arizonaclockco.com', 'http://planetamexicomarkham.com', 'http://www.aguilashidawayaz.com', 'http://www.drweksberg.com', None, 'http://www.allenlawaz.com', 'http://JodiAnngel.com', 'http://www.wineanddesign.com/clevelandwest', None, 'http://haircutmenbayviewandwellingtonauroraon.ca', 'http://www.essentialhealingcu.com/#!contact-info/c8gg', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.nirvc.com', None, None, 'http://www.timhortons.com/ca/en', 'http://www.viperlaw.com', '1592314689', 'http://www.acernovillasapartments.com', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'https://local.safeway.com/safeway/az/phoenix/3132-e-camelback-rd.html', 'http://popeyes.com', 'http://www.hexterspub.com', 'http://www.michaelsrockyriver.com', 'http://bugweedmart.com/stores/tempe/', 'http://www.thethirdplacesportsbar.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://www.kingdomofcleaning.com', None, '1592314725', 'https://www.vbiaz.com', 'http://www.wolschool.org', 'https://theniteowl.ca', None, 'http://nolbu.ca', 'http://www.saludbeershop.com', 'http://www.heavenlyblissweddings.com', 'http://www.mirage.com/shopping/the-beatles-shop.aspx', 'http://www.lakewoodgardencenter.net', 'http://www.centralcatholichs.com', 'http://www.berewickfamilydentistry.com', None, 'https://www.mistermoneybags.com', None, None, '1592314763', 'https://arizona.weidner.com/apartments/az/phoenix/mozaic-at-steele-park-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', None, 'http://www.kfc.com/storelocator/Default.aspx?address=5249+E+Brown+Rd%2CMesa%2CAZ', None, 'http://www.canadianthriftstores.com', 'http://adultmart.com?utm_source=yelp&utm_medium=social&utm_campaign=yelptest&utm_content=url', None, 'http://robertostacoshop.com', 'http://prestigebilliardsaz.com', None, 'https://www.hendersonproperties.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280191177&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://www.aramarkuniform.com/our-locations/aramark-uniform-services-phoenix', 'http://www.southwestplumbingandrepair.com', 'http://www.pickeringperformance.ca', 'http://www.easydrinkeasygo.com', 'http://www.supreme-cleaners.biz', None, 'https://www.ekdarrowhead.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, None, 'http://www.laurelhighlandsmeadery.com', 'http://www.sweetconnectionsoh.com', 'https://www.rubios.com', 'http://www.presscafe.com', None, None, None, 'http://www.lolitascantina.com', 'https://www.montecarloinns.com/downtown-markham-suites', None, 'http://www.thewinchester.net', 'http://www.jjtuckerinsurance.com?cmpid=L022_BLM_0006', 'https://twomenandatruck.com/movers/wi/madison', 'https://sunwest-auto-repair.business.site', None, 'http://www.lalimos.ca', 'https://www.sparc.vegas', 'http://onceuponachildconcord.com', 'http://meandmyyogurt.com/', 'http://www.bohncycleshop.com', 'http://www.heroesonline.com/heroescon/', 'https://www.walmart.com/store/7062/gastonia-nc/whats-new', None, 'https://surfthegreats.org', 'http://www.cynthiaschinese.com', None, None, None, 'http://locations.atipt.com/chandler-az', 'http://www.tempemortuary.com', 'https://www.harlowdentalnc.com', 'https://www.choicehotels.com/ohio/middleburg-heights/comfort-inn-hotels/oh439/rates', 'https://concrete.susd.org/schools/desert-canyon-es', None, 'https://www.extraspace.com/storage/facilities/us/arizona/chandler/1000000272/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'https://www.drkindt.com', None, 'http://www.tntscafe.com', 'https://www.dietzfloralstudio.com', None, 'http://westviewwater.org/', None, 'http://littlecaesars.com/MobileLocations/tabid/483/location/53590/Default.aspx?id=MTQwNDAwMDU%3D', 'http://www.idealcoffee.ca', None, 'http://www.familydollar.com', None, 'https://www.drlesani.com', None, 'http://www.tasteittours.com', 'https://www.azfamilylawattorneys.com', 'https://www.wellsfargo.com', 'http://cakerysquare.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'https://www.cricketwireless.com', '1592314936', 'http://www.recworldlv.com', None, 'http://azsuntops.com', 'http://indie88.com/', 'http://www.heroburgers.com', 'http://pawsvetclinic.com/', 'http://www.junkbrothersaz.com', '1592314958', None, 'http://www.myvillasatdesertpointeapartments.com', 'https://www.northitalia.com/locations/scottsdale-az-kierland-commons/', None, 'http://www.timhortons.com/', 'http://www.poorboytire.com', '1592314976', 'https://www.allureattempe.com', 'https://lasvegas.benefitbrowbars.com', 'http://www.cewcvegas.org', 'http://calle-8-restaurant-lounge.business.site', 'http://firstchoice.com/salondetail/default.asp?salonid=5068', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://homeinspectionscalgary.ca', 'https://www.omotrading.com', 'http://www.arizonahairco.com', 'http://webbsworldoffitness.com', 'http://www.charlotterusse.com', None, 'https://www.lowes.com/store/MI-Monroe/1074', 'http://www.mobile-depot.ca', None, None, 'http://thestandardoncollege.com/', None, 'http://hondatronics.com/', 'http://www.gustoballantyne.com', 'http://leesatamember.com/locations/tempe/', 'http://www.crystalclearpools.biz', 'http://maidz2clean.com', 'http://katespade.com', 'http://www.tasteofmediterranean.ca/', 'http://www.themresort.com/dining/terzetto.html', None, 'https://www.hondawest.net', 'http://barkavenuespaw.ca', None, 'http://www.andorracreditrepair.com', None, '1592315062', 'https://www.icwheelsllc.com', None, None, 'http://www.detoxbodycleanse.com', None, None, 'https://patients.unityps.com/contact/mesa-az-pain-clinic-find-treatment-options-for-your-chronic-pain/', 'https://www.az.aaa.com/automotive/car-buying', 'https://www.gostorageone.com/self-storage/nv/las-vegas/durango-rhodes-ranch', 'http://www.pureandsimple.ca', None, 'http://www.stonewallinstitute.com', None, 'https://www.services.gov.on.ca/locations/locationDetail.do?id=11475', None, 'http://penncoveeatery.com', 'http://www.schillersapothecary.com', None, 'http://www.goodwillaz.org/', None, None, 'http://www.lakeparkcare.com', None, 'http://www.gamestop.com', 'https://www.mgmgrand.com/en/nightlife/Centrifuge.html', 'http://www.behindthemask.com/', 'https://www.fordonfifth.com', None, 'https://www.gwhaz.com/properties/olive-grove-canyon-series/', None, 'http://www.yogenfruz.com', None, 'http://www.liveatsantierra.com', 'http://www.torontorentingguide.com', 'http://www.prada.com/', 'http://www.dollaboutique.com', None, 'http://longbranchfandc.com/Contact.html', 'http://www.eyeoptions.com', None, None, None, 'http://www.pcdroncall.com', 'http://www.beckerzarlinglaw.com', 'https://www.walmart.com/store/2767/mesa-az/details', None, 'http://www.thelovestore.com', None, None, 'https://www.circuscircus.com/en/adventuredome.html', 'http://solkitchenaz.com', 'http://www.swoozies.com', 'https://fatmanplumbingpro.com', None, 'http://www.charlotte.bcycle.com', None, 'https://www.sobeys.com', 'http://www.numotion.com', 'https://hemorrhoidclinicofarizona.com', 'http://ambianceboutique.org/', 'http://radioshack.com', None, 'https://www.bromley-apts.com', 'http://www.wow1day.com/locations/house-painting-scottsdale/', 'http://mcithedoctorsoffice.ca/patients/42-clinic-Whitby', None, None, 'http://www.fruitfulmarket.com', 'https://www.wyndhamhotels.com/hotel/52967?tel=18666154223&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52967', 'http://perspectiveswellness.com', None, 'http://www.smartmouthlv.com', 'https://www.officedepot.com/storelocator/az/phoenix/officemax-6319/', 'http://smithspharmacy.com', 'http://www.puresalonaz.com', '1592315248', None, 'http://ilwmassage.com', None, 'http://www.rocknrollmaterials.com', 'http://www.aeschbachautomotive.com', None, 'http://byondyogurt.com', 'http://www.hesslandscapenursery.com', 'https://www.warbyparker.com/retail/madison/401-state-st', 'http://www.ibclawfirm.com', 'https://www.woodstreamvillageapthomes.com', None, 'http://www.petgroom.ca', 'http://www.newlookusa.com', 'http://www.horndawgsbbqpickering.com', 'https://www.stefanmann.com', '1592315291', 'https://libertylock.com', 'http://www.polaricepeoria.com/', 'http://www.integritypools.com', 'https://www.monroevilledodgeram.com', 'http://www.scnm.edu/', 'http://www.thebrinklounge.com', 'https://www.24hourfitness.com/gyms/las-vegas-nv/molasky-active', None, None, 'http://www.senecapainting.com', None, None, None, 'https://www.convenientautoservices.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.enmax.com/', None, 'http://www.zaragozajewelry.com', 'http://heralasvegas.com/cqlashes/', '1592315337', 'http://www.regencydevelopers.net', 'https://www.autozone.com/locations/ca/concord/5267-clayton-rd.html', 'http://themayanclublasvegas.com/', 'http://www.atyourcurb.com', 'https://www.matrixmg.ca', 'https://fineartsdentistry.com', None, 'http://www.azbeemer.com', None, 'http://foxspizzaplumboro.com', 'https://www.wrightcars.com', 'http://www.stemsoaps.com', 'http://www.gamesunl.com', 'http://www.bar-c.ca', 'http://www.thewonderartists.com', 'http://www.myfathershousetoday.com/', 'http://pierandco.net', None, None, 'http://www.avenuemotel.ca', 'http://www.torontopubliclibrary.ca/hou_az_sws.jsp', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://desiburrito.com', '1592315396', None, None, 'http://www.c6toptrim.com', 'http://thespraygun.com', None, None, None, 'http://www.khansalar.ca', 'http://www.wetwillies.com/Locations/Charlotte.html', 'http://www.metrolexus.com', 'https://www.bangastudios.ca', 'http://www.heartcenterofnv.com', None, 'http://www.backandbodyhealth.com', None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.bistrodivino.com/', 'http://www.vino100phoenix.com', 'http://www.balkanfoods.ca', 'https://www.essenceofsaigon.com', None, 'http://www.citylocksmithpittsburgh.com', 'http://www.rehabdetailing.com', 'https://tiffanystowingllc.wixsite.com/tiffanystowing', 'http://www.spectaclelovesyou.com', 'https://www.pinotspalette.com/woodmere', 'http://www.prestigenailsalon.com', None, 'http://eyeconsultantsaz.com', 'http://www.petersenjohnson.com', 'https://www.gormanevap.com', None, None, 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', None, 'http://www.cleannfreshcleaning.com/', None, None, 'http://www.northstarchevy.net', 'http://theloftpilates.com/', 'https://us.louisvuitton.com/eng-us/point-of-sale/usa/louis-vuitton-las-vegas-wynn?utm_source=yelp&utm_medium=organic&utm_campaign=store_listing_storepage', 'http://www.redroxapartments.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', '1592315506', 'http://www.blastfitness.com/?utm_source=yelp&utm_campaign=indianschool&utm_medium=displayurl', None, 'https://www.charmingcharlie.com/stores/details?fbclid=IwAR2iVQG7_fMOeTbff-jnFBIBUoJ6zTqolugguTMj5OSr19367S2YCqjPoZo&stid=107', 'https://www.hpb.com/072', 'https://www.heinens.com/Heinens-of-Avon', None, None, 'http://www.autryseptic.com', 'http://Www.greencleanersllc.com', None, 'http://www.littlecaesarsinternational.com/cafr/Restaurants/tabid/1190/Default.aspx?id=NDc5NDAwMDE%3D&location=DOLLARD+DES+ORMEAUX%2CPQ+H9H+2A4%2C+Canada', 'http://www.parkdalevets.com/', 'http://www.sedonaatlonemountain.mgproperties.com', 'http://www.embassysuitesconcord.com/rocky-river-grille', None, None, 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', None, 'https://www.avis.com/car-rental/location/CAU/US/OH/Cleveland/CLE', 'http://www.hibachijapan.com', None, 'https://www.zeppestavern.com', None, 'http://gap.com/', 'http://www.backyardtaco.com', 'http://www.soaglass.com', 'http://www.originalcupcakes.com', 'http://concessionroad.ca/', 'http://www.themeatdepartment.ca', '1592315574', 'https://www.walmart.com/store/1857/mentor-oh/details', 'http://www.celebrity-hair-extensions.ca', 'http://www.charlotteindianrestaurant.com', 'http://bikramdowntown.com/', 'http://greatlifewellness.ca', None, None, None, None, None, 'https://www.hilton.com/en/hotels/gstnchx-hampton-charlotte-gastonia/?SEO_id=YELP-HP-GSTNCHX', 'http://erindalerestaurant.com/', None, 'http://www.jrslawnmaintenance.com', 'http://www.ladiraspa.com', 'http://www.dairyqueen.com', 'http://www.atlwings.com', 'http://www.bigjimfixmycar.com', None, None, 'https://www.aa.com', 'http://banana-leaf-catering-and-take-out.business.site', 'http://eattrattoria.ca/', None, None, None, 'http://www.airmaxxofcharlotte.com', 'http://www.bdjrealty.com', 'http://www.absolutetattooclt.com', None, 'https://www.melrosepharmacy.com', None, 'http://www.premierfitness.ca/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'http://www.tropicalsmoothiecafe.com', 'http://www.patoubistro.com', None, 'http://www.simplecures.ca', None, None, 'https://ad.doubleclick.net/ddm/clk/434420485;236814625;g', 'http://www.jamesonspubs.com/ne/', 'https://www.cornelius.org/125/Arts-Center', 'https://www.bannerhealth.com/locations/peoria/banner-health-clinic-86726', None, 'http://charlotte.mosquitojoe.com', 'http://cigarwarehouse.vegas', None, 'http://maxsold.com/Canada/Ontario/GTA/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-toronto&utm_term=permanent&utm_content', 'http://www.tomandjerrysbistro.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, None, 'http://www.pawssalons.com', 'http://www.elranchero-phoenix.com', None, 'http://www.neonlvpm.com', 'https://www.thejoint.com/nevada/las-vegas/montecito-marketplace-36001', '1592315721', None, 'http://wickedchili.ca/', 'http://cashnmore1.com', None, None, 'http://www.instarz.com', 'https://locations.theupsstore.com/az/glendale/20118-n-67th-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://stores.maccosmetics.com/us/az/phoenix/2502-east-camelback-road', 'https://www.cleanjuice.com/locations', None, 'http://www.charmeck.org', 'http://www.theolivesalon.com/', 'http://lknautorepair.com/', None, None, '1592315755', 'https://storelocations.ae.com/us/nc/pineville/11025-carolina-place-pkwy.html', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.baseline-locksmith.com/', None, 'http://www.familyautocarelasvegas.com', None, None, None, None, 'http://www.shapedbrowandbeauty.com', 'http://stlouiswings.com', 'http://www.geaugaparkdistrict.org/parks/observatorypark.shtml', 'http://www.ccsalonandspa.com/', None, None, None, None, None, 'http://cornerstore.com/StoreHome/1674', 'https://www.pizzazzpizza.com', 'http://www.losguaca-moles.ca', 'https://www.ifixitusa.com', '1592315805', 'http://www.racewaycarwash.com', 'http://www.thevegashandyman.com', 'http://www.azsneeze.com', 'http://www.khoraksupermarket.com', None, '1592315822', 'http://www.jonesfamilydentistry.com/', 'http://www.arizonadigestivehealth.com/locations/north-valley-endoscopy-center', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, 'https://order.pizzapatron.com/menu/phoenix-indian-school-road?utm_source=Yelp&utm_medium=Order&utm_campaign=Ordering', 'http://www.globalexoticcarrentals.com', 'http://www.bmwnewmarket.ca', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1491+Som+Center+Road-Mayfield+Heights-OH-44124/storeid=3343?cid=ps_ylp_2020', None, 'http://www.losfavoritostacoshop.com/', 'http://www.ontree.ca', 'http://www.trishsells702.com', None, None, 'http://www.madcitymusic.net', '1592315865', 'http://www.dunkindonuts.com', 'http://www.papajohns.com/', 'http://www.vicentina.ca', None, '1592315878', 'http://www.bondstreetwines.com', 'https://dg-landscaping-llc.business.site', None, None, None, None, 'http://www.VegasHomeSold.com', 'http://www.einsteinbros.com/', None, 'https://creativecappuccinoinc.com', 'http://2wrenchesautomotive.com', None, 'http://www.healthsouth.com', None, 'http://www.vanityvaultcalgary.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1212+South+Greenfield+Road-Mesa-AZ-85204/storeid=5026?cid=ps_ylp_2020', 'https://www.aquasafeswim.com/swim-lessons/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Gilbert-Ad', 'https://www.stanleysteemer.com/?utm_source=yelp&utm_medium=referral&utm_campaign=yelp_branch_ws_ad', 'https://p3mg.org', 'http://www.thetiptoptavern.com/', None, None, 'http://dreamhometoronto.ca', 'http://www.revitasize.ca', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592315938', 'http://www.marybrowns.com/', 'https://www.schoolhouseyoga.com', 'http://businesslawyergilbert.com', 'http://www.leatherlikenew.com', None, None, 'http://jbseatabite.com/', 'http://www.coldfusionrestaurant.com/', 'http://www.thehideouttoronto.com', 'https://www.bannerhealth.com/locations/sun-city-west/banner-health-center-85743', None, None, '1592315970', 'http://www.thenapoleonclub.com', None, 'http://www.saratogaapts.com', None, 'http://www.goodyearaz.gov/residents/parks-/neighborhood-parks/loma-linda-park', None, 'http://www.bojangles.com', None, None, None, None, 'http://www.scorpionchef.ca/', 'http://www.agsmllc.com', None, 'https://www.westerndental.com/en-us/find-a-location/arizona/chandler/3170-n-arizona-ave', 'http://www.freshfrybread.com', 'https://advancedvisioninstitute.net', None, 'http://www.conns.com/store-locator/nevada/las-vegas-89030', None, None, 'http://www.cuginositalia.webs.com', None, 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', 'http://racheldavisfinearts.com', 'http://quickfixgaragedoorservice.com', None, None, 'http://brasseriekensington.com/', 'http://www.marriott.com/LASFS', None, None, None, '1592316047', 'http://www.shelterinsurance.com', None, '1592316056', None, 'https://paulmitchell.edu/cleveland', 'https://www.orangetheory.com/en-us/locations/arizona/phoenix/10810-north-tatum-boulevard-suite-108/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.dillards.com', 'http://www.maid2kleen.com/', 'http://www.aurabycashewandclive.com', None, None, 'http://www.rsvpparty.com', 'http://arizonahairco.com', None, 'http://www.LVreo.com', 'http://www.theliftfactory.com', 'http://www.nikkistyleslv.com', None, 'http://maxontowershairsalon.com', None, None, 'https://valleyymca.org/chandler-gilbert', 'https://occasions4.us', None, 'http://www.brighton.com/', 'http://www.thelovestore.com', 'https://www.deseretindustries.org/locations/365548', 'http://www.eddyfruitfarm.com', None, 'https://www.keithheatingandcooling.com', None, 'http://derrick-balsamo-flooring-and-more.business.site', None, 'https://barrospizza.com', 'http://potbelly.ca', 'http://www.rtosullivans.com/', 'http://www.teonnasfloraldesign.com', 'http://reliablehomeworks.com', 'http://www.preciseliceremoval.com', None, 'http://cedarroomcigars.com', 'http://www.showandtelltees.com', None, 'https://danforth.modoyoga.com', 'http://www.kideweknot.com/', 'http://vistamedicalgroupaz.com/', None, 'http://www.clarkcountynv.gov/depts/ccdc/pages/default.aspx', None, 'http://www.wrdisplay.ca', None, 'http://www.babybumpultrasound.com', 'http://www.heatherglengolf.com', 'http://www.greatclips.com/salons/5555', None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=2021&localechange=1', 'https://www.matthewsautomotiveandtowing.com', None, None, 'http://www.yorkcinemas.ca', 'http://www.nomorerubbish.com', 'http://dorispoolspa.com', '1592316206', '1592316208', None, 'http://www.tourguys.ca', None, None, 'http://gatewayacademy.us', 'https://moreliascafe.com', 'http://www.centercitygreen.com/', None, 'http://homewoodsuites3.hilton.com/en/hotels/alberta/homewood-suites-by-hilton-calgary-airport-alberta-canada-YYCHWHW/index.html?SEO_id=YELP-HW-YYCHWHW', 'https://www.fischerspestcontrol.com', 'http://www.starskycanada.com/', None, None, 'http://www.perfectfitforyou.com', None, 'http://www.theantlerroom.com/', None, 'http://www.fiveguys.com', 'http://www.timhortons.com', '1592316257', 'http://zentacousa.com', 'https://dermahealthinstitute.com', None, 'http://www.ziarecords.com', None, 'https://www.bergerallied.com/cleveland-movers/', 'https://en.greengrotto.ca', None, 'http://www.cornerbakerycafe.com/', 'http://louiesultracleaners.com/', 'http://www.realtyexecutivesphoenix.com', 'https://risasdental.com/find-a-location/desert-sky/?utm_campaign=LocationPage&utm_medium=DesertSkyYelpWebsite&utm_source=Yelp', None, None, None, 'https://www.genesismedical.org/location/Passavant-Office', 'https://www.maidcomplete.com/house-cleaning-phoenix.php', 'https://www.hilton.com/en/hotels/pitktqq-distrikt-hotel-pittsburgh/?SEO_id=YELP-QQ-PITKTQQ', None, 'http://www.azshademasters.com', None, 'http://www.themaaz.com', 'http://www.fifiandme.net', 'http://www.azendospecialists.com/meet-us/meet-dr-walker/', 'http://www.madcrushwinebar.ca', None, 'http://www.paeseristorante.com/', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.lukesdrugmart.com/', 'http://www.customfedora.com', None, 'https://justskinaz.wixsite.com/mysite', 'http://sudforno.com', 'https://www.choicehotels.com/arizona/tempe/rodeway-inn-hotels/az083/rates', 'http://gallaghersaz.com/', 'http://www.viarail.ca', None, 'http://www.jodymaroni.com', 'http://www.homegoods.com', 'http://www.helzberg.com', 'http://www.wrightortho.com/', None, None, 'http://www.jppancake.com/', 'http://bellygoddess.com', None, 'http://www.PhoenixPinnacleFarms.com', None, 'https://locations.wendys.com/canada/qc/laval/122-st.-martin-blvd.', 'https://www.anytimefitness.com/gyms/2943/Glenshaw-PA-15116/?utm_source=yelp&utm_medium=local', 'http://www.ashleyfurniture.com', 'https://www.t-mobile.com/store-locator/nc/charlotte/whitehall-corner?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.taratarot.com', 'http://www.fairdme.com', '1592316399', None, None, None, 'http://www.aveda.com', 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', 'http://www.yifangtea.com.tw/en/index.php', None, 'https://www.walgreens.com/locator/walgreens-6649+morrison+blvd-charlotte-nc-28211/id=1376', 'http://lolaslasvegas.com/', 'http://www.lawsonfamilyplumbing.com/', 'http://www.vincenthairdesign.ca', 'http://foodtime.ca', None, 'http://www.swisschalet.com', 'http://www.sexyshineauto.com', None, None, None, 'http://www.littledarlingsvegas.com', 'https://www.autozone.com/locations/az/chandler/1025-n-arizona-ave.html', 'http://www.cimexcontrol.com', None, 'http://www.mastermeats.com', None, 'http://chargedlegalservices.ca', 'http://www.suncountrylandscape.com', 'http://www.lincolnprep.greatheartsacademies.org', 'http://ads.yorkbbs.ca/gangzaimeishi/', 'http://www.zwatsonpiercing.com', 'http://southdownchiropractic.com/index.html', 'http://www.mylakesaharapartments.com', None, None, None, 'http://www.matthewsappliance.com/', None, None, '1592316494', 'http://www.pnc.com', None, 'http://www.thespokeeasyclt.com', None, '1592316506', 'http://badmothercluckers.com', 'http://chocolateshops.sees.com/az/mesa/chocolate_shops_mesa_az_az007.html', 'http://www.springrolls.ca', 'http://horhuttreeexperts.com/index.html', 'http://badgercafelasvegas.mybistro.online', None, None, 'http://www.djssmokeshopaz.com', None, 'http://www.banfield.com/veterinarians/az/gilbert/gil?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://erichamiltontowing.com', None, None, '1592316539', 'http://www.bojangles.com', 'https://www.gypsyinkstudio.com', 'http://www.gonsteadspine.com/', 'http://www.chefslegacy.com', None, 'http://www.drleedy.com', 'https://ollyshoes.ca/pages/etobicoke-store', 'http://www.muahbeauty.ca', None, 'http://www.modernhairjunkie.com', 'https://cortland.com/apartments/university-center/', 'http://www.teatrader.com/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1212+South+Greenfield+Road-Mesa-AZ-85204/storeid=5026?cid=ps_ylp_2020', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.alleghenycoffee.com', 'https://piratesandprincesss.business.site', 'http://www.torontobartending.com', 'http://www.prestigeautomall.com', 'http://www.indianmotorcyclecharlotte.com', None, 'http://www.awareness.massagetherapy.com', 'http://stlouiswings.com', 'https://www.madradish.com', 'http://www.thehappybakers.ca', None, 'http://www.knight.academy/knight-academy-goodyear', 'http://www.thebullmarketstore.com', 'http://www.stellarossa59.com', 'http://www.papajohns.com', 'http://www.customgranitemasters.com', None, None, 'http://www.halinascafe.com', None, None, 'http://islandtimefloats.com', 'http://www.scottsdale-pizza.com', None, 'http://getsolarize.com', 'http://www.vegasgamerepair.com/', None, None, 'http://www.banfield.com/veterinarians/nv/las-vegas/smm?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://local.biglots.com/nc/matthews/1643?zcp=pd_local_yelp', 'http://www.beachcliffdental.com', None, None, None, None, 'https://www.supercuts.com/locations/pa/pittsburgh/shadyside-plaza-s-highland-haircuts-8953.html', 'https://smiledirectclub.com/smileshops/mesa-stapley-center/?utm_campaign=yelppaid&utm_medium=cpc&utm_source=yelp&utm_content=mesa', 'http://www.lenasnails.net', 'https://www.chagrinchiro.com', None, None, None, 'http://massageblissvegas.com', 'https://www.americaschoiceinspections.com', None, None, None, 'http://acleanexpression.com', None, None, 'http://www.1stscottsdaledental.com/', 'http://www.pastapomodoro.com', 'https://mr-wong.business.site', 'http://www.lynchautobody.com', None, 'http://www.vwrichmondhill.com', 'http://www.fye.com', 'http://www.bistrorougeyyc.com/', None, 'http://www.poopcafe.ca', None, 'http://ww2.chandler.k12.az.us', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.victoryelectronics.com', 'http://ribsandburgers.com/us/locations/las-vegas-nv/', 'http://www.jerseymikes.com/20199/Belmont-CA', None, None, 'https://local.fedex.com/az/phoenix/office-5048/', 'https://www.orangetheory.com/en-us/locations/nevada/henderson/10271-eastern-ave-103-105/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.ultimatecrc.com', 'http://www.amhurst.net', 'https://www.homedepot.com/l/Rocky-River/OH/Rocky-River/44116/3847?cm_mmc=seo-yelp&', None, 'http://www.omazzii.ca', 'http://madisonsnyc.com', 'http://treepro.us', 'https://www.perfectsheenpro.com', '1592316781', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://www.homedepot.com/l/East-Liberty/PA/Pittsburgh/15206/4136?cm_mmc=seo-yelp&', 'http://www.ameliospizzeria.com', None, 'http://www.leticolibri.com', None, '1592316798', 'https://www.jimstrans.com', '1592316802', 'http://clickserve.dartsearch.net/link/click?lid=43700040271614279&ds_s_kwgid=58700004686038588&ds_url_v=2', 'http://www.mellah.ca', 'http://azmedspallc.com', None, 'http://www.vainandluxe.com', 'http://www.annazjamesrl.com', None, '1592316820', None, 'http://mypickapart.com', 'http://www.bankofamerica.com', None, None, 'http://www.ohioceramic.com', 'https://www.amfam.com', '1592316840', 'https://precisionoralsurgery.com', 'http://maisnailsandlash.com', 'http://www.motherearthmaids-oc.com', 'https://flowercompany.ca', 'http://www.giovannisparma.com', 'https://dentalhomeaz.com', 'http://www.saiaffilms.com', 'http://www.rsvprealty.com/', None, None, 'https://www.target.com/sl/tempe/319', 'http://www.azdesertlocksmith.com', 'http://www.prettysickbeauty.com', 'http://www.addictedcoffeebar.com', 'https://www.vivint.com/ppc/protect?exid=207432&utm_source=yelp&utm_medium=display&utm_campaign=yelp_q3&utm_content=KkvvJki4kY-MkUMFuEpRdQ', 'http://www.reids.com', 'https://www.casamiascottsdale.com', None, 'http://www.ihg.com/holidayinnexpress/hotels/us/en/peoria/phxpe/hoteldetail', '1592316894', None, 'http://halloffamecollectables.com', 'https://www.escapeok.com', 'http://www.autonationvolkswagenlasvegas.com', 'http://www.flamingopalacecalgary.com', 'http://www.bedbathandbeyond.com', 'https://oceanspa5.wixsite.com/oceananailsanddayspa', 'https://www.payless.com/stores-location/NV-LAS-VEGAS-5798.html', 'http://www.shearsynergy.com', 'https://cobblestone.com/?utm_source=yelp%C3%8A', 'http://miamicafephx.com/', 'http://www.smoghut.com', 'http://www.kcstarnesautobody.com/', None, None, 'http://www.alexhairsalon.com/', 'http://www.mandalafloral.com/', 'http://www.banfield.com/veterinarians/nc/charlotte/bky?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, 'https://www.madvapes.com', 'http://sakebarkushi.ca/', 'http://www.1550apartments.com', None, 'https://locations.mrtire.com/oh/northfield/10235-northfield-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'http://www.hop-and-vine.com', None, 'http://www.maxi.ca', 'http://valleykeyconnection.com', 'http://www.suiterautomotive.com/', None, 'http://www.opticgallery.com', 'https://www.aaautocarelv.com/locations/400-simmons-st/', 'http://www.goodshepherdpet.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044280205718&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.vegasclubhop.com', None, 'http://aaaship.com', None, '1592317966', 'http://www.starbucks.com/store/8223/', 'https://www.lapisandoak.com', 'http://www.sunkingcleaners.com/', 'http://www.virgilsbbq.com/locations/las-vegas/', None, None, 'http://deserthillsmail.blogspot.in', 'http://robertostacoshop.com', 'http://www.bonitasphx.com', None, 'https://www.starbucks.ca', 'http://www.devilsmartini.com', 'https://www.smallmangalley.org/bars/coffee-espresso/', None, None, None, None, None, 'http://www.wetnwildlasvegas.com?utm_campaign=2019&utm_medium=Profile&utm_source=Yelp', '1592318013', 'http://www.bluedogrv.com', 'https://streakpatrol.com', 'http://www.northyorkeyeclinic.com', None, None, None, None, 'http://www.barque.ca/bar', None, 'http://korea-chinese-food.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.14108.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:14108', 'https://www.vucare.com', 'http://www.bk.com', 'http://thepainterslounge.com', '1592318055', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YULAL', 'https://www.boulevarddodge.com', 'http://www.arribamexicangrill.com/', 'http://www.foxyfruitbowls.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.thebarbershops.com', 'http://storelocator.pepboys.com/pepboys/stores/chandler/chandler/00735', None, 'http://www.hipkidspediatrics.com', 'http://www.buybuybaby.com', 'http://www.armitageice.com', 'https://smartstopselfstorage.com/storage-locations/usa/nevada/las-vegas/smartstop-self-storage-4851-e-bonanza-rd', 'https://www.angelvet.com/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Euthanasia', 'https://apricotlaneboutique.com/store/orangevillage/', 'http://www.kegsteakhouse.com/en/locations/ON/toronto/mansion-keg/', 'http://www.gogreenbodypaint.com', None, None, 'http://www.ambassadorcigars.com/', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=12179&localechange=1', 'http://www.gravitysoundbar.com', 'http://www.millaspa.com', None, None, 'http://www.theroofmedic.com', None, 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', None, 'https://www.diamondkitchenandbath.com', 'http://www.broomsandroses.com', None, None, '1592318141', 'http://www.ultimatewash.com', 'http://www.expertsonsight.com', 'http://www.starbucks.com/store/9298/', 'http://www.starbucks.com/store/10759/', 'https://twotalldistilling.com', 'http://www.ricetogo.ca', None, 'https://www.batteriesplus.com/store-locator/pa/pittsburgh/batteries-plus-186?utm_source=yelp&utm_medium=local&storecode=186', 'http://www.mesavalleycollision.com', 'http://heartcenteraz.com/locations/central-phoenix-office', 'http://www.countrycheesecompany.com', 'http://www.sonorandesertplumbing.com', 'http://www.nationwideplumbingllc.com/', 'https://www.accentondecatur.com', None, 'http://www.minnecisristorante.com/', '1592318181', None, None, 'https://www.floristmesaaz.com', 'http://www.maccosmetics.com', None, None, 'http://www.awesometotsparty.com', 'http://www.lebistrofit.com/', 'http://www.drcallison.com', 'http://gemandbeadmallmesa.com', None, '1592318207', 'https://www.dairyqueen.com/ca-fr/Locator/Detail/2034', 'https://www.dipnailbarhorizon.com', None, 'http://www.colorectalconsultants.com', 'http://locations.harristeeter.com/nc/concord/202/', 'http://www.strongmanappliances.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://locations.jambajuice.com/ll/US/AZ/Scottsdale/15686-N_-Frank', None, None, 'https://amerihome-mortgage-refinance-center.business.site', 'https://www.mgmgrand.com/en/hotel/the-mansion.html#/Dining', 'http://www.bojangles.com', 'https://www.healthyskinmd.com', 'https://www.petsmart.com/stores/us/oh/willoughby-store0526.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://livingkitchen.com', 'http://www.bikepgh.org', 'http://adminrugs.com/', 'http://republicofhair.com', 'http://www.ritasarrowhead.com', 'http://www.tastyjoesaz.com', 'http://www.rustysdeli.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.nationwideautoslv.com', '1592318272', None, 'http://www.bellaslechon.com', 'https://www.truecarewellness.com', None, 'http://www.MomDoc.com', 'https://www.sprouts.com/stores/details/-/store-details/view/store/501/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://www.iloveindoorsoccer.com', 'http://www.bebe.com', 'http://www.arizonapestsquad.com', 'http://www.truckingoodfood.com', 'https://www.papajohns.com', 'http://www.secureparking.com', 'http://www.landrysseafood.com', 'http://www.alvinailey.org/', 'http://northharborclub.com/', 'http://Timhortons.com', 'http://www.autonationnissanlasvegas.com', 'http://www.autoactionaz.com/', '1592318318', None, None, None, None, 'https://www.universityvillagecharlotte.com', 'https://www.haircutmendenvernc.com', 'http://www.justbetterair.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.samscarwashkl.com', None, 'http://suncitydogs.com', 'https://www.thepointeatthefoothills.com', 'http://www.cppittsburghwest.com', None, None, 'http://www.maac.com/florida/tampa/colonial-grand-at-lakewood-ranch?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://downeastbasics.com', 'http://ohmypaw.com', 'http://figotoronto.com', 'http://www.smgaz.org', None, None, 'http://www.hiitlifefitnesslv.com', 'https://moxies.com/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', 'https://doubletree3.hilton.com/en/hotels/pennsylvania/doubletree-by-hilton-hotel-and-suites-pittsburgh-downtown-PITDTDT/index.html?SEO_id=YELP-DT-PITDTDT', 'https://www.napaonline.com', 'http://www.usatlasmovers.com', '1592318392', 'http://www.winestore-online.com', 'http://zoneathleticperformance.com', None, 'http://joeysofchicago.com', 'https://www.t-mobile.com/store-locator/az/chandler/chandler-fashion-center?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://mensloungeaz.com', None, 'http://cell-doc.com/locations/tech-repair-concord-mills-nc/', None, 'http://www.theartofshaving.com', None, 'http://www.thewilleyville.com', 'http://atasteofgreeceaz.com/', 'http://www.acupunctureaz.com', 'http://crumblcookies.com', 'http://www.mississauga-fleamarket.com/index.html', '1592318433', None, 'https://www.screenmobile.com/Locations/US/Arizona/Phoenix/62', 'http://laveendental.com', 'http://www.sevenbrothersburgers.com', None, 'http://www.toysrus.com/family/index.jsp?camp=MISC:yelp:store:page:tru:111910&categoryId=2255956', 'https://www.lnlspaw.com', None, 'http://www.sarkujapan.com/#home', None, 'https://merlincustomhomebuilders.com', 'http://www.jasonspronk.com?cmpid=M33Q_BLM_0006', 'http://www.stevenburkelaw.com', 'http://www.beveragebarbers.com', 'https://tocayaorganica.com', 'http://pennellogallery.com/', 'http://genevievehansen.com', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.usmtgs.com/home.html', 'http://uplservices.com', 'http://www.mississaugachineserestaurant.ca/', 'http://www.madisongeeks.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592318492', 'http://www.twelve27.com', 'http://www.lvaudiocustoms.com', 'http://www.koob.ca', 'http://mckenneychevrolet.com', 'http://www.echairlv.com', 'https://eweknit.co', 'http://www.DLund.com', 'https://allcareobgyn.com', 'https://kids.discoveryplace.org/huntersville', 'http://www.bowlology.com', 'http://local.firestonecompleteautocare.com/pennsylvania/monroeville/397-mall-circle-dr/?lw_cmp=IYP_YPC_MLP_19461', 'http://www.imaginationsunltd.com', 'http://www.flyingmonkeypub.com', '1592318530', None, 'https://mahoneylawoffice.net/', 'http://www.proautocareaz.com', 'http://BFLSalon.com', 'http://www.dollartree.com/', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', 'https://www.nellaonline.com', 'http://www.thermal-medics.com', 'https://chocolatory.kitkat.ca', None, 'http://www.badbeatbrewing.com', 'http://www.shainestevenson.com?cmpid=PRHU_BLM_0006', 'https://www.opendoor.com', None, 'http://www.petaldustbakeshop.com', 'https://www.solasalonstudios.com/salon-professional/brittany-miller1', None, None, None, 'https://www.thecenterlv.org', 'http://vacationinnphoenix.com/', 'https://www.clevelandfed.org', 'http://www.hardrockhotel.com/relax/reliquary-spa', 'http://www.thisisafeast.com', None, None, '1592318595', 'https://ad.doubleclick.net/ddm/clk/434265604;236814625;g', None, 'http://www.changinghands.com', 'http://www.johnsonfitness.com', 'http://www.zappos.com/lv_outlet.zhtml#blvdmall', 'http://www.mistercarwash.com/', 'http://www.putsys.com', 'http://vaporice.com/?fbclid=IwAR0m6W7npEn63A2nWczT3BnY_BWBWsWR35Qn19UNYKl_TlRVdTfrCnjvf8Q', 'http://www.minchias.com', 'https://guilin-cuisine.business.site', 'http://brightwayphotography.yolasite.com/', None, None, 'http://www.timhortons.com', 'http://www.accins.net', 'http://www.abettergaragedoor.com', 'http://www.hawkestonecrossfit.com', 'http://www.sunnysidemarket.ca', 'http://www.cras.edu', 'http://www.thehamptonsaz.com', 'http://www.estrellapediatrics.com/', 'http://www.soniquehairdesign.com', None, None, 'http://olenliving.com/communities/arizona/highland-groves-at-morrison-ranch/', None, None, 'https://adnanmachado.wixsite.com/bikerepair', None, 'http://www.deltaco.com', 'http://palookavillechili.com', 'https://mrsub.ca', 'http://www.acehardware.com/store-details/04252', 'http://prairiepgh.com/', 'http://info.tradesecrets.ca/store-locations-and-reviews/vaughan-mills/', 'http://www.skyzone.com/Charlotte', 'http://www.phoenixchildcare.com', 'http://thesaguaro.com/scottsdale', 'http://www.charliesmainevent.com/', 'https://patients.unityps.com/contact/glendale-az-pain-clinic-stop-suffering-from-chronic-pain/', 'http://www.hmv.ca/', None, None, 'https://locations.wendys.com/united-states/co/aurora/3435-salida-st', 'https://www.discounttire.com/store/nv/henderson/s/1300?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.familyvet.com', None, 'http://www.papamurphys.com/', 'https://jetpetresort.com', None, None, 'http://www.thehandyguysaz.com', 'https://www.heistbrewery.com/the-cans', 'https://trust.dot.state.wi.us/cscfinder/cityCountySearch.do?city=Madison', None, 'http://www.portlandsphoenix.com/', None, None, 'http://sergiorossi.com', 'http://www.azstatefair.com', 'http://www.royallube.ca', None, 'http://www.hooters.com', 'http://www.skinfitnesslv.com', None, None, None, None, 'http://www.zaraspaandhair.ca/home1/', 'http://www.rereading.ca/', 'https://locations.panerabread.com/az/scottsdale/8777-n-scottsdale-rd.html', None, 'http://www.danklebrunsonleedds.com/', 'http://www.twistbarandgrill.com', 'http://chinchinstreetside.com', 'http://www.searshomeapplianceshowroom.com/home/az/surprise/6997', 'http://smile-white.ca/', 'http://www.thairoom.ca', 'http://www.fleetfarm.com', 'http://www.vetcoclinics.com', 'http://www.reveuro.com', 'http://houseofcues.com', 'http://vegasgaypoolparty.com/', 'http://www.nirvanatheflavoursofindia.com/', None, 'http://www.shopakr.com', 'http://streetwiseautomotive.com', 'http://www.timhortons.com/', 'http://www.sunflowerpetsupply.com', None, 'https://locations.dennys.ca/AB/CALGARY/248179', 'https://curaleaf.com/stores/nj', 'http://inspirekidsmontessori.com/', 'http://www.daynnightautogroup.com', 'http://www.antoniusbros.com', 'http://www.leespalace.com', 'https://locations.monro.com/oh/solon/33605-solon-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://www.eaglerideraz.com', 'http://www.queensmaidcleaningservice.com', 'http://www.actionpotentiallab.ca', None, 'http://www.entouragevegas.com', '1592318823', 'http://www.LakeViewHomesLLC.com', 'http://www.breadbasketinc.com', 'https://ccleaning00.wixsite.com/carpet-steamers', None, 'http://www.corktowndesigns.com', 'https://www.clubpilates.com/scottsdalepromenade', 'http://www.mcdougallgroup.com', None, 'http://www.autozone.com/storelocator/storeLocatorMain.jsp?targetPage=storeLocatorMapHours&store=406', 'http://bbqcreole.com', 'http://locations.lifelabs.com/details/ON/Etobicoke/22', 'http://www.healthykidzpediatricsmesa.com', None, 'http://www.mimosaspirit.com', 'http://www.viplimoslv.com/', None, 'http://www.hottopic.com', 'http://frillylilly.ca/boutiques/frilly-lilly-mission', None, 'http://www.cycle-solutions.com', 'https://bluestonelane.com/coffee-shops/downtown/', 'https://www.petittigardencenter.com/index.php/locations/bainbridge', 'http://www.comicsnmore.com/', 'http://www.aztaxiphx.com', 'https://magasinage.villagedesvaleurs.com/qc/dollard-des-ormeaux/villagedesvaleurs-magasin-doccasions-2082.html', None, 'https://skinnybusreviews.com', None, 'http://www.mrbrewstaphouse.com/locations/madison-wi/', None, 'http://scentforyou.ca', 'http://www.potbelly.com/UW?utm_source=ExtNet&utm_medium=organic&utm_campaign=Yext', 'http://www.alphaeliteaz.com', 'http://www.petplanethealth.com/stores/village-plaza/', 'http://advancedhandwrist.com', 'http://www.pinnacleinternalmedicine.com', 'http://www.spinpickering.com', 'http://ellisplasticsurgery.ca', 'http://www.shawarmahousevegas.com', None, 'http://www.airdoctorofthecarolinas.com', 'http://www.socleanlv.com', None, None, 'http://www.gigglesplayland.ca', None, 'http://www.beautyextraordinaire.com/', None, 'http://www.nevadaimaging.com', 'http://www.mcentenolaw.com/', 'http://www.chuckfranklin.com', 'https://www.myazac.com', 'http://soullessperformance.com', None, None, 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', 'http://www.bioscreenclinical.com', 'http://www.littlecaesars.com/', 'https://www.qualityglassnv.com', 'http://www.kitchengallerymadison.com', None, 'http://www.brainstormescapes.com', 'https://tintonthespot.com', None, 'http://www.benfenlon.com', None, 'http://www.allianceurgentcare.com/index.html', 'https://agents.allstate.com/lydia-hernandez-north-las-vegas-nv.html', 'https://www.midas.com/phoenix/store.aspx?shopnum=1109&dmanum=684001', '1592318990', 'https://stores.savers.com/az/peoria/savers-thrift-store-1107.html', None, 'https://azfirehouse.com', 'http://capturedmomentsaz.com', 'http://www.nourish123.com', 'https://www.acbyroberts.com', 'http://www.lknpetgrooming.com', 'http://slslasvegas.com/katsuya', 'http://www.hairvanabyahreumlee.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.londonbespokeclub.com', 'https://locations.jackinthebox.com/us/az/goodyear/520-n-estrella-pkwy', 'http://pizza.dominos.ca/Calgary-Alberta-10108', '1592319026', '1592319029', 'http://www.truenorthstores.com', 'http://cigarandtobaccoshop.com', 'http://www.adencamera.com', None, 'http://drinkrealwater.com', 'http://campbowwow.com/fort-mill', None, 'http://patcatans.com', 'http://www.papajohns.com', 'http://theshoecompany.townshoes.ca', 'http://www.timhortons.com/', 'http://www.kidscovepreschool.org', None, 'https://netdivorce.com', 'https://www.pastalears.com', 'https://www.waxworkshairremovalscottsdale.com', 'https://www.trilliumeyecare.ca', 'http://www.want.ca/', 'http://mesaaz.gov/things-to-do/parks-recreation-commercial-facilities/pools/rhodes', 'http://www.mrosmow.com/', None, None, None, 'http://www.prlrlounge.com', 'http://www.yourlinktohealth.com', None, 'http://www.tacologist.net', 'http://www.woodnicklaw.com/', 'https://www.abnerheating.biz', 'http://www.getwellbar.com/', '1592319101', None, 'http://www.aaaaffordablepolygraph.com/', None, None, 'http://www.pauls-auto-repair.com', 'http://www.detailshomeboutique.com', 'http://iloveyogurtys.com/', 'http://www.nosecreekphysiotherapy.com', 'http://www.gopenske.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.busybhousecleaning.com', 'https://www.staples.com', None, 'https://www.no1kitchenohio.com', 'http://www.campaniacafe.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/9100+West+Sahara+Avenue-Las+Vegas-NV-89117/storeid=8812?cid=ps_ylp_2020', None, None, None, None, 'http://www.ghost-armor.com/storelocator/index/view/id/103/', 'http://www.kidzfirstpediatrics.com/', None, None, 'https://www.9round.com/fitness/Scottsdale-AZ-x1189', 'https://www.atouchoflvspa.com', 'http://www.wecarefwc.com', 'http://www.kitintl.org', 'http://www.sprinklerworld.com', 'https://www.ritasfranchises.com/PennHills', None, 'https://www.kooltempo.com', 'http://www.pittsburghperiodontists.com', None, None, '1592319179', 'http://www.ryerson.ca/ric/', 'http://www.kelseys.ca', 'http://www.psacademyarizona.com', 'http://www.safeway.com', None, 'http://www.jandelandscape.com', 'https://www.starbucks.com/store-locator/store/6920', None, None, 'https://www.hollywoodheroes.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.crossfitcharlotte.com', 'https://www.mppinfusion.com/locations/tyler/', '1592319212', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZTC', 'https://chocolateshops.sees.com/nv/henderson/chocolate_shops_henderson_nv_1nv001.html', None, None, None, 'https://www.simpsonpropertygroup.com/apartments/charlotte-north-carolina/the-encore-southpark', None, None, 'http://www.siegelsuites.com/rent-apartment-las-vegas/sierravista-las-vegas-apartments.php', 'http://www.premierhealthaz.com/', None, 'https://locations.crackerbarrel.com/oh/willoughby/525/', None, 'http://www.trumphotels.com/las-vegas/las-vegas-poolside-dining.php', '1592319247', None, 'http://www.friendlymoverspgh.com', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', '1592319256', None, 'https://www.bestwestern.com/en_US/book/hotel-rooms.36124.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:36124', 'https://www.arworkshop.com', 'http://www.gangnamsushi.ca', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.nvhomeinspections.com', 'https://www.karateaikido.com', 'http://www.desertroseobgynaz.com', None, 'http://www.99ranch.com', 'http://www.learningcurves.ca', 'https://alacrityestatesales.business.site', 'http://pitakouzina.com', 'http://peakskiandboard.com', 'http://veincliniclasvegas.com', 'http://bk.com/', 'http://www.cowbellrestaurant.ca', 'http://www.bodyinbalanceyoga.com', None, None, 'https://www.projectfish.ca', None, 'http://lpg2u.com/', 'http://www.dunkindonuts.com', 'http://www.mistersparkyelectricnv.com', 'https://www.peytonparkerinsurance.com?cmpid=dk1j_blm_0006', None, 'https://www.rackroomshoes.com/?utm_source=Yelp%20&utm_medium=localsem%20&utm_campaign=20170330_RRS%20&utm_content=webtraffic', 'http://www.ellivenspa.com', None, 'http://www.getitdun-rite.com', 'http://www.hotel32lasvegas.com/', 'https://www.rentmeadowglen.com', 'http://www.zone7foods.com', None, None, None, None, None, 'https://www.labcorp.com', 'https://www.pigglys.com', 'https://www.rcwilley.com/location/Nevada/Las-Vegas-Henderson-Nevada-Furniture-Store?utm_source=yelp&utm_medium=referral', 'https://www.evolvesvc.com', 'https://arizona.weidner.com/apartments/az/phoenix/the-hawthorne-2/', None, 'https://eweknit.co', None, 'https://www.wyndhamhotels.com/hotel/12236?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seca:12236', 'http://www.monsoonroofinginc.com', 'http://www.tangtangtangvegas.com', '1592319383', 'http://www.starbucks.com/store/9298/', None, 'http://www.redbrickpizza.com', 'http://www.linebergerdentistry.com', 'http://www.cleanandshine702.com', 'https://www.kekou.ca', None, 'http://www.romeospizza.com', 'http://www.tuffyleonastreet.com', 'http://www.londonautowerks.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.joesmidnightrun.com', None, 'http://petgroomingcleveland.com', 'http://l.macys.com/biltmore-fashion-park-in-phoenix-az?cm_mmc=Yelp_Stores-_-Phoenix-_-n-_-451&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Phoenix_451&m_ac=yelp_stores&m_ag=n', 'http://www.greatclips.com/salons/3063', 'http://www.randmautorepair.com', 'https://stores.advanceautoparts.com/az/phoenix/3246-west-indian-school-rd', 'http://www.artisticsalon.ca', 'http://www.maneeventlv.com/', 'http://portasdomarbarandgrill.com', 'http://www.fitbodyweightloss.com', None, 'http://www.arcadiacounselingcenter.com', 'http://www.azexpest.com', 'https://www.athome.com/store-detail/?StoreID=Wisconsin-Madison%20West&utm_source=yelp&utm_medium=paidprofile', '1592319453', 'http://www.secondcup.com', None, 'http://www.allstardriving.ca', 'http://www.5thstreetarcades.com', 'http://oilchangers.ca/oil-changes-north-york-901-sheppard-ave-west', None, None, 'http://lkwmotors.net', '1592319471', 'http://www.pjwhitehardwoods.com/', None, 'http://www.healthyskinaz.com', None, None, 'http://www.tricountykitchensinc.com', 'http://www.pizzafire.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=14238', 'http://wonderlandbakery.com', None, 'http://powercoreplus.com', 'http://www.grasspal.com', 'http://bucontractors.com/', 'http://mobileonewireless.com/', 'https://simonmed.com', 'http://www.ramada.com/hotels/arizona/glendale/ramada-at-arrowhead-mall/hotel-overview', 'http://www.redrockinsure.com', 'http://www.cruciblesocialclubs.com', 'http://www.xicenter.com/', None, 'https://www.silvervalleypoolandsparepair.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.halibuthouse.ca', 'http://eikonicmane.com/', None, 'http://www.joygarveypllc.com', 'http://www.ppsc.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://walmart-eyedocs-lasvegas.com/', None, None, 'http://truhitfitness.com/central-scottsdale/', 'https://rudysstrudel.com', None, 'http://www.cbac.com/tega-cay?utm_source=Social&utm_medium=Yelp', None, None, 'http://kaldiamondbuyers.com', 'http://www.poppiesplantofjoy.com', 'http://www.wrightav.com', '1592319571', None, None, None, 'http://www.paradisecarpetcleaningaz.com', 'https://peoria.legacytraditional.org', 'https://www.LeaLanasBananas.com', 'http://www.shiatsuworks.com/', None, None, 'https://www.vaughan.ca/services/recreation/community_centres/maple_cc/Pages/default.aspx', 'http://ontiscurbandlandscape.com/', 'https://www.gloriajeans.com/locations/west-towne-mall/', 'http://www.marriott.com/hotels/travel/cltco-courtyard-charlotte-concord', 'http://www.meltingpot.com/charlotte/welcome', 'http://www.fhsohio.com', 'https://www.theexchange.com', 'http://www.acrossthepondphx.com', 'https://barbecuesgalore.ca/pages/calgary-south', None, None, None, 'http://www.affderm.com', 'http://advantagepestcontrol.co', None, None, None, 'http://www.timhortons.com/', 'http://www.desertskymall.com', None, 'http://www.advancedmanualtherapy.com/', None, None, 'http://twizted-manez-beauty-barber.business.site', 'http://order.papajohns.com/', 'http://www.myamazone.com', 'https://thaiexpress.ca', None, 'http://www.thegoodguysauto.com/', 'http://store-locations.underarmour.com/nv/las-vegas/67/', 'http://springmastergaragedo.wixsite.com/springmaster', 'http://healthykidscarelv.org', '1592319672', 'https://www.walgreens.com/locator/walgreens-1745+e+southern+ave-tempe-az-85282/id=1197', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://cityhunt.com/team-building-cities/las-vegas-scavenger-hunt/', 'http://www.montyscentralvac.com', 'http://orangeleafyogurt.com', 'http://www.prettyinpittsburgh.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.officedepot.com/storelocator/az/surprise/officemax-6689/', 'http://www.oolongteashop.ca', 'https://desertmoverslv.com', 'http://hot975phoenix.com', None, 'http://storelocator.staples.ca/stores/en_CA/ON/Etobicoke/12', 'https://www.hungryhowies.com/store/hungry-howies-01814?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=1814&utm_content=Website_Link', 'https://www.klinkecleaners.com/locations/dane-county-locations/fitchburg', 'http://www.santanchiro.com', None, 'https://my.clevelandclinic.org/locations/directions/288-bainbridge-urgent-care', 'http://www.sunstatecardiology.com', None, 'https://locations.panerabread.com/pa/tarentum/2021-butler-logan-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'https://www.northitalia.com/locations/las-vegas-nv/', None, 'http://www.petplanethealth.com/stores/country-hills-town-centre/', 'https://www.autorepairshopharrisburgnc.com', 'http://www.chinesefoodgallery.ca', 'http://www.diversifiedroofing.com', 'https://www.destinationhotels.com/tempe-mission-palms', 'https://modpizza.com/locations/indian-trail/?utm_campaign=yelplistingbusiness&utm_medium=referral&utm_source=yelp', 'https://www.stircrazycomedyclub.com', 'http://www.shimmernailsandhair.com', None, None, 'http://www.flavourhousevapes.com', 'http://www.glendaleaz.com/foothillscenter/index.cfm', None, None, None, None, None, 'https://ad.doubleclick.net/ddm/clk/434333894;236814625;n', 'http://www.clubvivalasvegas.com/', 'http://www.cnlawlv.com', None, 'http://eastwaypaint.com', 'https://www.wellsfargo.com', 'http://www.808hmp.com', 'https://www.wellsfargo.com', None, 'http://www.deciopasta.com', 'http://us-militarysurplus.com', 'http://www.homesteadhotels.com/Reservations/SelectRoom.html?sid=bd6aa337-d961-4bec-b278-fb228e121c09&', None, 'http://www.parkland.edu/aviation', 'http://www.starbucks.com/store/9334/', 'http://www.marcs.com/stores/marc-s-avon-grocery-store-44011.aspx', 'http://finechiropractic.com', 'http://www.bmwtoronto.ca', 'http://www.axeandhatchet.com', 'http://www.starbucks.com/store/12853/', 'http://fujiyamacalgary.com', 'http://www.acepropertymanagementnv.com', None, 'https://www.signaturestyle.com/locations/oh/strongsville/best-cuts-first-federal-commons-haircuts-60027.html', None, 'http://www.jaapgh.org/care/skilled-nursing-rehabilitation', 'http://jvnailsspa.com', '1592319847', None, 'http://www.corneliusdrafthouse.com', None, None, 'http://jaythegroomer.com/', None, 'https://stores.bareminerals.com/az/glendale/us-9913/', 'http://progrexion.com', 'http://phoenixphotolab.com', None, 'http://tributarycle.com', 'http://www.greenhomesolutions.com/charlotte-nc', 'http://elegantgaragesale.com/', None, None, 'https://www.petpeoplestores.com/aurora.html', 'http://donutconnection.com/', 'http://www.aaacityplumbing.com', 'http://www.mashumashu.ca', 'http://fiveguys.com/', 'https://www.smithsfoodanddrug.com/stores/details/706/00334', 'http://www.aplusmobilepetgrooming.com/mobile-pet-grooming-richmond-hill', 'http://www.firstusacarpetcleaning.com', 'http://www.mypinkhare.com', 'http://usps.com', 'http://pizzapino.us', 'https://locations.wafflehouse.com/az-phoenix-1489', 'http://www.arbys.com', None, 'http://www.autoglassofphoenix.com/', 'http://www.csihi.com/', 'http://www.ampm.com', 'http://www.drzeyes.com', None, 'http://www.thepeacefulsoul.com', 'https://www.quicknclean.net', 'http://forestcitybrewery.com', 'http://www.santannaturalmedicine.com', None, 'https://stoughtonlumber.com', None, None, None, 'http://www.growopboutique.com', 'https://www.lab11.ca', 'http://www.kirklands.com', 'http://www.seraphicmassage.com', 'http://www.cityviewdentaltoronto.com', 'http://www.dfcporsche.com', 'https://www.carstar.com/locations/wi/verona-15020/', 'https://www.truwest.org', 'https://www.gamestop.com/store/us/co/lakewood/1672', 'https://www.kellycardenassalon.com', 'http://www.nextcare.com/locations/az/phoenix-thomas/?utm_source=Yelp&utm_medium=Local&utm_campaign=phoenix_thomas', 'http://www.birthyourroots.com', 'https://lawhutson.com', '1592319986', 'http://prosperitycleaners.net', 'http://www.cupcakecastle.net', 'http://carriageparkapts.com/', 'http://www.regalnails.com', 'http://www.soccercrazy.com', None, 'http://www.thebutlerdiditllc.com/', None, 'http://realdonutsvegas.wix.com/theshop', None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', 'http://www.morantesdds.com', 'https://www.smithsfoodanddrug.com/stores/details/706/00311', None, '1592320022', 'http://www.riposahairsalon.com', 'http://www.la-z-boy.com/Southeast/Pineville', 'http://www.apachetrailswapmeet.com', 'http://www.originwellness.ca', 'http://www.tph.ca/print/toronto-yonge-st-eglinton-ave', 'http://www.salonestique.com', None, '1592320042', 'http://www.narwhalboutique.com/', 'http://www.timhortons.com', None, None, 'http://www.quiktrip.com/', '1592320057', 'http://hendersonhearingcenter.com', 'http://www.mesaterracehoa.com', 'https://locations.sonicdrivein.com/pa/tarentum/1010-village-center-drive.html', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/10720+West+Bell+Road-Sun+City-AZ-85351/storeid=9217?cid=ps_ylp_2020', 'http://www.cccnevada.com/our-physicians/medical-oncologists/james-sanchez-m-d/', 'http://www.amazingjourneys.net/', 'http://sipyard.com', 'https://www.thedockonqueen.com', None, 'http://www.tatummedical.com/', None, None, 'http://www.bk.com', 'http://www.celebritytanning.com', 'http://azfow.com/', 'http://thelittlegymgilbert.com', 'http://www.corerestaurant.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.reliabletransmissionrepair.com', 'http://taquerialajacky.weebly.com', 'http://www.mrcombo.co', 'http://www.irontribefitness.com/locations/dilworth/', None, 'https://www.smalv.com/OurCenters/HealthCareCenters/Montecito', 'http://www.rickhartmanplumbing.com', 'http://www.theorysalon.com', 'https://www.bridgmanlaw.com', 'http://www.drivingarizona.net/', 'http://www.traderjoes.com', 'http://heatdziczek.com', None, 'http://www.silverstatecu.com', 'http://www.saladcreations.net', None, 'http://www.mih.vegas', None, None, None, 'http://www.healthplusclinic.ca/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'https://www.pteglv.com/locations/sean-patricks/ann-simmons/', 'http://wink24.net', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.steinmart.com', 'http://www.yogurtys.com/storelocator/store/4672/', 'https://www.evaair.com/en-us/index.html', 'https://akitasushibradford.wordpress.com', 'http://www.anytimefitness.com', 'http://www.bk.com/restaurants/pa/n-versailles/1901-lincoln-hwy-3030.html', 'http://www.bluboho.com', 'http://www.redwingshoe.com', 'http://www.burgerjointlv.com', 'http://www.dominos.com', None, 'http://www.4cmedicalgroup.com', 'http://www.ticketsandtours.com', 'http://www.7-eleven.com/?yelp=29384', None, None, 'http://fornocultura.com/', 'https://www.matthewlopezlawyer.com', 'http://www.calgaryfarmersmarket.ca/vendors/wild_fire_wings/#vend', 'http://wholelifedentistry.com', 'https://www.thebrick.com/pages/store-calgary-sunridge', 'http://www.relaxingwellness.ca', None, None, 'http://www.cmnh.org', 'https://locations.dennys.com/WI/MADISON/248083', 'http://www.floorseasons.com', 'http://radioshack.com', 'https://www.minorikchiropractic.com', 'https://www.dollarselfstorage.com/storage-locations/nevada/north-las-vegas-self-storage.php?utm_source=yelp&utm_medium=cpc&utm_campaign=general', 'http://www.sparockhill.com', None, 'http://www.chickenmaster.com', None, 'https://www.fistoffusionislandgrill.com', 'http://ilfornello.com/locations/oakville-2', 'http://1stresponserestores.com', 'http://www.lemongarden.canadachinese.ca', 'http://www.expressurgentcares.com', 'http://www.forbiddenaz.com', None, 'http://www.Vegasbugs.com', None, 'http://www.365mechanical.com', 'http://www.alltogethermoversaz.com', 'https://www.budgetdumpster.com/phoenix-az-dumpster-rental-arizona.php', 'https://pizzanova.com', 'http://www.lascalacreamery.com/', 'http://Calicafelasvegas.com', 'http://www.c-osa.com', None, 'http://www.hottopic.com', 'https://www.pokibing.com', 'http://www.nellies.ca', None, None, None, 'http://www.tropicalsmoothiecafe.com', 'http://www.southcentrevw.com', None, None, None, None, 'https://www.centennialmoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.allurenailsscottsdale.com/', 'http://www.sportracks.com', 'http://www.starbucks.com/store/14160/', None, 'http://www.bk.com', None, None, None, 'http://www.modwaterrestoration.com', 'http://locations.traderjoes.com/nc/charlotte/742/', 'http://www.rumbi.com', 'http://www.cranstouncourt.com', None, 'https://neonbrand.com/locations/las-vegas-digital-marketing/', 'https://www.cakemeawaygastonia.com', None, 'http://www.southernresources.com', None, None, None, None, 'http://www.glvpm.com', None, 'http://www.dulvickdentistry.com', 'http://midlandrea.com', 'http://www.desertsedgerv.com', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', 'http://www.tacorrito.ca/', '1592320384', 'http://superllanteramexico.com/SuperLlanteraMexico/Inicio.html', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.bunmee.net', 'http://southwestbicycles.com/', 'http://avis.com', 'http://www.expressionsdental.ca', None, 'https://www.tempe.gov/government/community-services/parks/golf-tempe/ken-mcdonald', 'http://www.whitehousemeats.ca', None, 'http://www.metrolinaperio.com', 'https://shop.nordstrom.com/st/nordstrom-southpark#restaurants?cm_mmc=yelp-_-ycm-_-rest-_-26750', 'http://cobblehaus.com', 'http://www.starbucks.com/store/9229/', None, None, None, 'http://belovedlily.com', 'http://www.bellashouseandpets.com', None, '1592320431', 'http://www.quakersteakandlube.com/', None, 'http://www.LiveatCornerstoneRanch.com', None, None, None, 'https://www.jerseymikes.com/9003', 'http://www.golfgalaxy.com', None, 'https://www.certifiedplumbingheatingcooling.com', 'http://www.bntazlaw.com', 'http://www.welashout.com', 'http://solterrafifthave.com', 'http://www.forefatherssteaks.com', None, '1592320466', 'http://www.arrowheadranchdentistry.com', None, 'https://www.bankofamerica.com/', 'http://www.ochathainoodlepa.com', 'http://www.mtc.gov.on.ca/en/ontarioplace/park_trails.shtml', None, 'http://www.amorartisbrewing.com', 'http://www.mcfarlandanimalhospital.com', 'http://www.romaitalianrestaurant.net/', 'https://www.drpancholi.com', None, 'http://www.richmondhilltoyota.com/', None, 'https://leechenbistro.com', 'http://www.vegasinspect.com/', None, 'http://www.scottcondiedentistry.com', None, 'https://locations.timhortons.com/ca/on/richmond-hill/1070-major-mackenzie-dr.html', 'http://splashndashlv.com', 'http://www.saxeortho.com', None, None, 'http://www.caninecompanionclinic.com', 'http://www.uniexpressnv.com', 'http://www.azmedweightcontrol.com', 'http://www.fixingspacesaz.com', None, None, 'http://reflectthesun.business.site', 'http://www.borobudursf.com', 'http://www.forever21.com', 'http://www.azsprinklerservices.com', 'http://www.FlyersDirect.com', None, 'https://villagespizza.com', 'https://mattas.com', 'http://www.starbucks.com/store/9298/', 'https://www.acfs2000.com', 'http://www.mohawkflooring.com/carpet-store/Las-Vegas_NV_89183/Fabulous-Floors?utm_campaign=MohawkYelpProgram&utm_medium=Web&utm_source=Yelp', 'http://www.mysticjourneyz.com/', 'http://www.arizonaeyes.net', 'http://www.altamesagolf.com', 'http://www.portagedocs.com', 'http://www.breyerlaw.com/office-phoenix.html', 'https://www.oldorchardinc.com', 'http://shuppesautoshoppe.com', 'http://www.bellissimolawgroup.com', None, None, 'https://www.sbarro.com/locations/galleria-at-sunset/', None, 'http://www.spurlock.illinois.edu', None, 'http://calgarymediclaser.com', None, 'http://www.sculpturecenter.org', 'http://phoenixarc.salvationarmy.org', 'https://info.superelectricphoenix.com', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.sohoframing.com', None, None, 'http://www.cobsbread.com/local-bakery/kingsland-calgary', None, 'http://www.starbucks.com', None, 'http://arizonacommunityfarmersmarkets.com/FM_HighStreet.html', None, None, None, None, 'http://www.macayo.com', 'http://www.boeboxing.com', 'http://www.charmeck.org/', 'http://projectmanagementacademy.net/cleveland/pmp-certification.php', None, 'http://www.jlpgh.org/?nd=wear_after_shop', None, 'http://www.fxfitnessclubs.com/broadview-heights', 'http://www.bloompediatricdentistry.com', None, None, None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Charlotte-NC-28206/780052/', 'http://www.winwinkungfu.com', 'https://www.choicehotels.com/illinois/urbana/sleep-inn-hotels/il418?source=pmfyelp&pmf=yelp', 'http://www.twpusc.org/crc/crc-home', None, 'https://locations.mrtire.com/pa/allison-park/4900-william-flynn-hwy?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.wliaz.com', 'http://www.cashamerica.com/SUPERPAWN-stores/AZ/PHOENIX/Pho01', 'http://www.pospisilfamilydentistry.com/', 'http://www.accruepartners.com', 'https://azprosteemers.wixsite.com/azprosteemersllc', 'https://find.shell.com/ca/fuel/10052988-68-st-32-ave-ne', None, 'http://www.inlandaquaticslv.com', 'http://www.thedrswolfson.com', 'http://www.mrsandwichlv.com/', 'https://drpennadc.com', 'http://www.harryrosen.com/store/Bloor%20Street', 'http://www.pizzanova.com/locations/markham.html', None, None, 'http://www.mrwaterheater.com', 'https://www.homedepot.com/l/S-Boulevard-Charlotte/NC/Charlotte/28217/3646?cm_mmc=seo-yelp&', 'https://mylocalmcds.com/willow-pass-concord', None, 'https://www.instylefurnitureinc.com', 'https://zoeskitchen.com/locations/store/nc/blakeney', 'https://www.carsmetics.com/auto-body-shop-charlotte', 'https://www.nike.com/retail/s/nike-factory-store-las-vegas-north', 'http://www.magiccitycustoms.com', 'https://littlecaesars.ca/en-ca/stores/48600201/3100-winston-churchill-blvd/mississauga/on/contact', None, 'http://gfautogroup.com', 'http://www.tatummedical.com', 'http://anisetapas.com/', 'https://smalv.com', 'http://www.Desertcanyonlv.com', 'https://www.1800packrat.com', 'https://vital4men.com/locations/peoria-az-testosterone-replacement-therapy-clinic/', 'http://www.independenttuning.ca', None, 'https://www.getgocafe.com/store/details?name=east-mckeesport-getgo', None, 'http://www.salontwobytwo.com', 'https://studiomoviegrill.com/Locations/NorthCarolina/EpiCentre?utm_source=yelp&utm_medium=organic&utm_campaign=yelp&utm_content=EpiCentre', None, None, 'http://www.carlylemanagement.com', 'https://www.valleyperinatal.com/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Website', None, 'http://masoniccleveland.com', None, 'https://www.blakeneydental.com', 'https://ccv.church/locations/avondale', 'https://www.premiumoutlets.com/outlet/aurora-farms', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'https://www.crossfitto.com', None, 'http://www.twinpeaklandscaping.com', None, None, 'http://www.justfresh.com', 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', None, 'https://cleveland.firebirdsrestaurants.com', 'http://www.americanfreight.com/?utm_source=yelp&utm_medium=social&utm_campaign=profile', 'https://americanmale.com/las-vegas/', None, 'http://www.wendys.com', 'http://www.azcarpetsource.com', None, 'http://www.myperfectclean.com', 'http://www.meltndip.ca', 'https://www.mccarran.com/', '1592320854', 'https://locations.timhortons.com/ca/on/richmond-hill/1070-major-mackenzie-dr.html', 'http://www.timhortons.com', 'https://www.laitnight.com', 'http://www1.toronto.ca/wps/portal/contentonly?vgnextoid=512d2271635af310VgnVCM10000071d60f89RCRD', 'http://www.vieweyecare.com/', '1592320868', 'http://www.timbersgaming.com', 'https://www.pizzaville.ca', 'https://www.personaltrainer-scottsdaleaz.com', 'http://www.pullapart.com/locations/cleveland-west.aspx', 'https://www.walmart.com/store/1598/phoenix-az/whats-new', 'http://revolt-studio.com', 'https://www.starbucks.com/store-locator/store/10362', 'http://www.relaxtheback.com', 'http://www.altasteelyardlofts.com/', 'https://www.kababkingnc.com', None, None, 'http://www.clubcorp.com/Clubs/Firethorne-Country-Club', None, 'http://johnnyvilleslugger.com/', 'http://www.lcbo.com', 'http://lasvegasluxuryrealestateagent.com', 'http://www.dolcegelato.net', 'https://www.maracayhomes.com', None, 'http://www.frigidairaz.com', 'http://www.midwoodflowershop.com', None, 'http://www.dottphotography.com', 'http://www.baierlsubaru.com/?=yelp_track', 'http://thai-sushi101.com', 'http://www.barbspreciouspups.com', None, None, 'https://www.gloriajeans.com/locations/monroeville-mall/', 'http://www.cannerycasino.com/dining/vinos-pizzeria', None, 'https://locations.vitaminshoppe.com/pa/pittsburgh/vitamins-supplements-pittsburgh-pa-496.html', None, 'https://percida.myportfolio.com', None, None, None, 'http://valleyobgyn.md', None, 'https://www.aamedicalonline.com', 'http://www.vegapowerpilates.com/', 'http://www.systemsearch.net', None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, None, 'https://www.firehousesubs.com/locations/nc/speedway-blvd', 'http://www.cudoggiedaycare.com', 'http://night-market-bar.business.site', 'http://www.sandyscatgrooming.com', 'http://www.flamesgymnastics.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.selliPhone.vegas', 'https://www.homedepot.com/l/Cave-Creek/AZ/Phoenix/85022/480?cm_mmc=seo-yelp&', 'http://www.pro-artdentallab.com', None, 'https://www.christmaslightsforyou.com/pages/christmas-light-installation-quote', 'https://planetsub.com', 'http://www.haircuttery.com', 'https://www.oaktree.vegas', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://elrinconnayarita.com', None, 'https://smoothieking.com/location/view?store=1555', 'http://mc849.yourkwoffice.com', 'http://www.pusateris.com/', None, 'https://www.greatlakeshealthohio.com', None, None, None, 'http://www.lateadas.com/', '1592321033', 'http://silvertoncasino.com/dine/wuhu-noodle', None, 'http://restaurants.applebees.com/oh/bedford/411-northfield-rd.html', 'http://www.animalhospitalverona.com/', '1592321045', 'http://www.cmlibrary.org/locations/branches.asp?id=6', 'http://www.collins-mehlingtransfer.ca', 'https://www.petsmart.com/stores/us/nv/las-vegas-store1153.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', None, 'http://www.lc21bistro.com', 'http://www.Vogelprep.com', 'http://www.khyberhalalfood.com', 'http://www.serpachrysler.ca', None, None, 'https://www.take5oilchange.com/locations/oh/cleveland-122/', 'https://www.thecoolingco.com/schedule-service?utm_campaign=TCC%20-%20Repair%20Appointments&utm_source=ppc&utm_medium=Yelp&utm_term=1st%20Campaign&utm_content=Schedule%20Appointment', 'http://www.liveten01.com?utm_medium=Listing&utm_source=Yelp', 'http://www.legendaryinvestment.com', 'https://movinonxpress.com', 'http://www.clevelandfoodbank.org', 'http://www.ihg.com/candlewood/hotels/us/en/madison/msnfb/hoteldetail', 'http://Lavatoryphx.com', None, 'http://sushibombusa.com', None, 'https://www.holtonwisepropertygroup.com', 'http://www.batterygiant.com', 'http://www.kimelchiropractic.com/', 'http://adfences.net', None, 'http://meatrestobutcher.com', None, 'http://www.theherbalclinicanddispensary.com/', 'http://www.angiesaesthetics.com', 'http://www.desertfootsurgeons.com', None, 'https://cortland.com/apartments/courtney-village/', 'http://local.firestonecompleteautocare.com/wisconsin/madison/6265-mckee-rd/?lw_cmp=IYP_YPC_MLP_358043', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.yoliesbrazilian.com', 'http://www.orleanscasino.com/dining/big-als-oyster-bar?disid=wmm_yelp_to_corporate_bigals_organiclink', 'http://www.7starlv.com', None, None, 'http://www.monroevillekia.com', None, 'http://sailplusnails.com', 'https://www.hilton.com/en/hotels/cltupgi-hilton-garden-inn-charlotte-uptown/?SEO_id=YELP-GI-CLTUPGI', 'http://www.prolocksmiths.com', 'https://vcahospitals.com/blue-cross-las-vegas?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Blue_Cross_Animal_Hospital=main_url', 'http://www.expertisebeauty.com', 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', None, 'https://www.park28apts.com', 'http://www.kathmandurestaurant.ca', 'http://www.starbucks.com/store/9334/', None, None, 'http://www.verdictridge.com/golf/proto/verdictridge/dining/dining.htm', 'http://valleyofthesunpoolservice.com', 'https://hardyspoolcare.com', 'http://www.vcultimate.com', None, 'http://www.timhortons.com/', None, 'http://www.elysiumofaz.com', None, 'http://www.lasvegasfit.org', 'https://stores.bestbuy.com/oh/north-olmsted/5140-great-northern-plz-s-279.html/?loc=ns100&ref=NS', 'http://www.nsumc.com', None, None, 'http://www.localchimneysweeps.ca', None, 'https://redrock.sclv.com/Dining/Feast-Buffet?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', 'http://www.kaffelive.com', 'https://www.sprouts.com/stores/details/-/store-details/view/store/501/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.motel6.com/en/motels.nv.las-vegas.1337.html', 'http://www.thebodyshop.ca/', None, 'http://ebqthaiicecream.business.site', 'http://www.hyderabadpalacegta.ca', 'https://locations.cinnaholic.com/ll/CA/ON/Thornhill/Promenade-Mall', 'http://www.teatreecafe.com/', 'http://www.mcdonalds.com', 'http://www.fatbastardburrito.ca', '1592321237', 'http://uptownvethospital.org', 'https://barrospizza.com', None, 'http://www.unleashedinthecity.com', 'http://phoenixeyebrows.com', 'http://electricalcontractorlasvegas.nv-biz.com', 'http://henry4sons.com', 'http://www.doucefrance.ca', 'http://www.asgard-steel.com', 'http://www.smogbusters.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://bigotires.com/Location/AZ/TEMPE/85284/004218/1/5ef102f5-6ad4-491f-a851-1c77187e1f7a', 'http://www.gabrielsrestaurant.ca', '1592321272', None, 'http://www.dos-diablos.com', None, None, 'http://www.bellagio.com/pages/din_shintaro.asp', 'http://www.memphischampionshipbbq.com', None, 'http://fuchsiaspa.com/high-street', 'http://castleplacechinesecuisine.weebly.com/', 'http://www.shulans.com', 'http://appletree-books.com', None, 'http://www.presscoffee.com', None, '1592321310', 'http://7eleven.ca/store-locator/33370', 'http://www.basilthaifusion.com/', 'http://www.lasvegasparty-bus.com', 'http://www.marbleslab.ca', 'http://www.progressive.com/locations/mayfield-heights-campus3/', 'http://www.kelliseyecenter.com', 'http://www.rosaspizzaplace.com/', 'https://mikesbeerbar.com', None, None, '1592321335', '1592321338', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3610+West+Anthem+Way-Phoenix-AZ-85086/storeid=9340?cid=ps_ylp_2020', 'http://realtyexecutives.com/Agents/Jonathan_Miller/', 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID117', 'http://GordonLawLV.com', 'http://arizonaappraisaladvisors.com', 'http://www.northeastfactorydirect.com', None, None, None, 'http://www.westendmeats.com', 'http://www.waxjewelrydesignstudio.com', 'http://www.striderite.com', 'http://www.mrchickencle.com', None, 'http://www.washtublv.com', 'http://www.luxorpaintinginc.com', 'https://altaskydental.com', 'http://adventuresmiles.com', None, 'http://freepeople.com', 'http://www.charleys.com', None, 'http://tasteandspicy.com', 'http://www.alicefazoolis.com', 'https://www.jetspizza.com/stores/north-carolina/matthews/920-park-center-dr?utm_source=Yelp-Ads&utm_medium=Yelp-Ads-SEO&utm_campaign=NC-008&utm_content=Website', None, 'http://athertonmillandmarket.com', 'http://www.dollar.com/Locations/gen.aspx?locationId=YYC', 'https://www.moonvalleynurseries.com/locations/northwest-las-vegas?utm_campaign=yelp&utm_source=yelp-nv&utm_medium=rancho', 'https://datangfootspa.com', None, None, 'http://www.mezza.ca', 'https://www.precisionmist.com', 'http://www.brimzofficial.com', 'http://www.bugworkspestcontrollasvegas.com', None, 'http://www.stpeterscatholic.org', None, None, None, None, 'https://www.paylesscar.com', None, 'http://www.alliancecomfortaz.com', 'https://dutchbros.com/?utm_source=tempe&utm_medium=yelp&utm_campaign=website_tempe', None, 'http://storelocator.staples.ca/stores/en_CA/AB/Calgary/54', 'http://www.menchies.com', None, 'https://onqfinancial.com/arizona/raintree-office', 'http://www.yogastrongstudios.com', None, 'http://www.madisonbrows.com/', 'http://www.goodwillaz.org/', None, 'http://www.wontonchainoodle.ca', 'https://www.acmestores.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.pizzahut.com/', 'http://www.meadowsmedicalgroup.com', 'http://www.simonandjoeseatery.com', None, 'http://www.foodcity.com', 'http://www.pensketruckrental.com/locations/ohio/madison/020624', 'http://www.bk.com', 'http://saltedcaramelcatering.com', 'http://www.flawlessfinishaz.com', 'http://www.beebes.com', 'http://www.biltmorecommonsdental.com/', None, 'http://www.uhhospitals.org/westlake', 'http://www.scottsdalehomestore.com', None, 'http://scarboroeastauto.ca', None, 'http://www.amtransporter.com', 'http://valentiacoffee.com', None, 'http://www.bagelbindelimenu.com', 'http://www.cedarbraegolf.com', None, None, 'http://www.adarpizza.com/', 'http://www.fastsigns.com/364', None, None, 'http://www.bojangles.com', 'http://www.ultranailboutique.com', 'http://enjoymusictoronto.com/', 'http://www.rccmassage.com/', 'https://tablesidegourmet.com', None, 'http://www.harborfreight.com/storelocator/location/map?zipcode_input=89032', 'http://www.ecoleconduite.ca', None, 'http://www.jiffylube.com', 'http://www.shopartmart.com', 'http://www.drleof.com', None, 'http://www.boarnwing.com', '1592321579', 'http://www.crossfittempe.com', 'http://www.majorleaguetow.com', 'https://www.nlvweightequipment.com', None, 'http://toyoschiro.com/index.php', 'http://www.clubraft.com', 'http://www.canadream.com/halifax', 'http://www.alphagraphics.com/centers/mesa-arizona-us291/', 'http://www.tehrankabab.ca', 'http://www.mcfarlandscustomcarpets.com', None, None, None, 'https://www.arco.com', 'http://www.helpling.com', None, 'http://storelocator.staples.ca/stores/en_CA/AB/Calgary/250', 'https://www.zaxbys.com/locations/nc/concord/7781-gateway-ln-nw/', 'http://www.clevelandcremationservice.com', None, None, 'https://www.checkcity.com/locations/nevada/tropicana-and-mt-vista/', None, None, None, 'http://www.insur4u.com', 'http://www.urgentair.com', None, 'https://www.mypctechs.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'http://www.empireserviceswest.com', 'https://www.expresspros.com/scharlottenc/', 'http://www.desertgemestatesales.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.marriott.com/hotels/travel/pittw-towneplace-suites-pittsburgh-airport-robinson-township', 'http://www.coolhandofagirl.com/', 'http://www.greenfieldnailsandspa.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://stores.shopjustice.com/az/glendale/girls-clothing-store-glendale-az-528.html', 'http://www.spot-onhomes.com', 'http://www.proactiveph.com/', 'http://1on1boxingfitness.com', 'http://organstoppizza.com/', None, None, 'http://bodybalancespa.com/', 'http://www.advantagehobby.com', 'http://www.fannyksalon.com', 'http://www.milanofoodworks.ca/', 'http://thecrowntheater.com/', None, None, 'http://www.sushimountain.com/', None, '1592321715', 'http://www.lasvegasblindsandsolarscreens4u.com', 'http://www.localfare.ca/', 'https://www.deerspringsmoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://www.broncosrestaurant.com', None, 'http://www.ihg.com/candlewood/hotels/us/en/las-vegas/laspd/hoteldetail', None, 'https://www.homedepot.com/l/N-Scottsdale/AZ/Scottsdale/85260/472?cm_mmc=seo-yelp&', 'http://www.trochefertility.com', None, None, None, '1592321747', 'http://www.atouchofrainnailspa.com', None, 'http://www.camelbackfamilydentalcare.com', 'http://nativetraditions.com', 'http://www.vueatcentennial.com', '1592321761', 'http://cutcleaners.com', None, 'https://rotech-granite-inc.business.site', 'http://www.northlandvolkswagen.com', None, 'http://www.remn.biz', 'http://greenforestfamilyrestaurant.net/', 'http://fromhockeytohollywood.com/', 'https://www.firebirdrvstorage.com', 'http://www.frysfood.com/', 'http://www.purplebulltavern.com/', 'http://mykeyport.com', None, 'https://locations.waxcenter.com/nc/huntersville/huntersville-northcross-0181.html', 'http://www.monocleoptical.vegas/', 'http://www.hm.com/us/store-locator#store=US0094', 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', None, 'http://quartieretempe.com', None, 'http://www.luxor.com/dining/dining_fusia.aspx', 'http://latrattoriacalgary.ca', None, 'http://www.eggsmart.ca', '1592321825', 'http://www.elysiabeauty.com', None, 'http://www.potterybarn.com/', 'http://www.americandentalcenters.com', 'http://www.quakerhillvet.ca/', None, 'http://www.jacobsgrandegroup.com', None, None, 'https://locations.churchs.com/az-phoenix-7235', None, 'http://stores.redwing.com/scottsdale-az', 'http://www.tempe.gov/Police', 'http://azpt.azbodybuilding.com', 'http://www.sixstarnails.com', 'http://www.secondcup.com/', None, 'http://www.timhortons.com', 'https://www.mountainviewpub.pub', 'http://www.tacobell.com', 'http://www.aurochsbrewing.com', None, None, None, 'http://www.rackroomshoes.com', None, 'https://www.higleyparkdental.com', None, 'http://www.burlingtoncoatfactory.com/store-details-Store-448--570-North-Stephanie-Street--Henderson--NV--89014-6612.aspx?from=89014&id=b4f9ac40-c5cf-4169-91d3-c072e36f7a85', 'http://www.miniso.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.pamperedpeopleaz.com', 'http://www.pittsburghsymphony.org/pso_home', 'http://www.7-eleven.com/?yelp=36154', 'http://www.tidedrycleaners.com', None, None, 'http://www.safelite.com', 'http://familynailsphoenix.com', 'http://www.theactlv.com/', 'http://www.imaginon.org', 'http://www.shell.com', 'https://www.walmart.com/store/2515/phoenix-az/whats-new', 'http://www.gentledentalwestchandler.com', 'https://www.lakewooddentalgroup.com', 'http://www.jimmarshbodyshop.com', 'http://www.blueskyeswellnesscenter.com', 'http://www.thebeerstore.ca/locations/danforthgreenwood', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.memoriespawnshop.com', 'http://www.peakdentallv.com', 'http://greatlakestheater.org', 'http://www.sincitybeer.com', 'https://www.target.com/sl/mccandless/1218', 'http://www.lovesinthehair.com', None, 'https://www.performancebike.com/bike-shop/store/charlotte', None, 'http://sapphirenailslv.com', None, 'http://www.avedainstitute.ca/index.php?/services/salon', None, 'http://www.discountautosales.co/', 'http://extremelightingandgrip.com', '1592321980', 'http://www.starbucks.com/store/14887/', 'http://www.bullseyecateringlv.com', 'http://stores.sunglasshut.com/us/az/tempe/2000-e-rio-salado-pkwy.html', None, 'http://www.scottsdalefarmtables.com', 'https://www.southstburger.com/location/st-clair-rushton/', None, 'http://www.vegansweettooth.com', 'http://fiveguys.com/', 'http://mapo-korean-bbq.business.site', 'http://www.balanceholistichairstudio.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://sataysate.com', 'http://www.macssushi.com', 'http://www.arizonaanimalactors.com/', None, 'http://www.littlecaesars.com', 'http://www.thelegendatbergamont.com', 'http://wyep.org', 'http://www.candidpixphotobooths.com/', None, 'http://pleasanthillsbarbershop.com', 'https://www.lowerysgarage.com', 'http://www.gallerystyles.com', None, 'http://www.vegas-motels.com', 'http://www.dairyqueen.com', 'http://timeshareexitteam.com', 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', None, None, None, None, 'http://www.pizzapizza.ca/', None, '1592322063', 'http://www.scottsdalecarservice.com', None, 'http://217inc.com', 'http://denkhadentistry.com', 'http://www.momandpoptaxshop.com', None, 'http://www.gamerepair.com/', 'http://www.arizonapoolcovers.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'https://www.ricesushibuffet.com', 'http://www.starbucks.ca', '1592322095', None, 'http://www.dentistryincharlotte.com/', 'http://www.scarboroughcc.com/', None, 'http://browsthreadingsalons.com', 'http://www.dignityhealth.org/stjosephs/services/cancer-center', 'http://www.loftandcellar.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXAB', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', 'http://www.aplusregistry.ca', 'https://www.MMbrows.com', 'http://patisseriekirin.com', 'http://www.infinitecarerx.com/', 'http://www.theeateryto.com/', None, None, 'http://www.parrotu.com', 'http://www.pawnnowaz.com/phoenix-85022', None, 'http://www.sears.com', 'http://www.curbsideblisscupcakes.com', 'http://www.mcbridecompanies.com', 'http://www.citgo.com', None, 'http://papadanstrains.com', 'http://www.wolfsonmedicalcenter.com', None, 'https://moxies.com/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', 'https://www.t-mobile.com/store-locator/nc/gastonia/shops-at-franklin-square?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://sunriserestaurantcharlotte.com', 'http://www.santanford.com', 'http://bonobos.com/guideshop', None, 'http://www.eatpizzapalermo.com', 'https://www.charlotteprogressivedentistry.com', 'http://www.sidelinesbg.com', 'https://www.bashas.com/stores/bashas-supermarket-mcdonald-granite-reef/', None, None, 'http://www.artagallery.ca', 'http://www.uniqtailors.ca', None, None, 'http://www.billystroyhillbistro.net', None, 'http://novellodesserts.ca/', 'http://www.wateroflifeschool.org', 'http://www.hotbambooaz.com', 'https://www.ice-canada.ca/en/?utm_source=yelp', 'http://www.oldtimecuisine.com', 'http://www.soggiedog.com', 'http://www.dranneshaw.com', 'http://www.st-sauveur-hotel-laurentides.com', 'http://www.sushikaya.com', None, 'http://samisgyros.net/', None, None, '1592322234', None, None, None, 'http://joeysurban.ca/locations/alberta/calgary/braeside.php', None, 'http://www.peacelutheranpreschool.org', None, 'http://www.wolleytaxi.com', 'http://www.johnsonfitness.com', 'http://www.thecupcakeryto.com', 'http://www.divasalonspa.com/', '1592322257', 'http://crosskeysinnpgh.com', None, 'http://www.masonslm.net', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, None, None, 'http://www.allprodjsaz.com', 'http://mvlcs.org/', 'https://www.veterinaryemergclinic.ca', 'http://doblowdrybar.com', 'https://www.kindercare.com/our-centers/monona/wi/071120?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=071120', 'https://www.enterprise.com/en/car-rental/locations/us/ca/glendale-s-brand-blvd-32vg.html?mcid=iyp:8368400', 'http://www.bouncearoundtown.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, None, 'https://www.circlek.com/store-locator/us/avondale/3-e-main-st/2700822', None, None, 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.ksbwexford.com/', 'http://www.sportshall.ca', 'https://www.supercuts.com/locations/pa/etna/etna-towne-center-haircuts-80365.html', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'https://www.millenniumhotels.com/en/scottsdale/the-mccormick-scottsdale/', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://www.nakedcitylv.com', 'http://www.arizonahairco.com', None, 'http://www.fivebelow.com', 'http://evkmselfdefense.com/martial-arts-classes/Arizona/Tempe/291', 'http://www.desertjewelobgyn.com/', 'http://www.pneustouchette.ca/', 'https://www.mirage.com/en/restaurants/fin.html', None, None, 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', None, None, None, None, 'https://www.getgocafe.com/stores/pa/pittsburgh/baum-blvd-getgo/3064', 'http://www.k1speed.ca', None, 'http://nappys.ca', None, 'http://nailgallerysalon.com', 'http://664tjbirrierialasvegas.cafecityguide.website', None, 'http://eastcoastcustard.com', 'http://www.gianteagle.com/home', 'http://adenshayoasis.com/', 'http://www.pattersonfarm.com', 'http://paintdepotcharlotte.com', 'http://www.corktowndesigns.com', 'http://www.allcads.com', 'http://www.omnidermatology.com', 'https://www.crunch.com/locations/ballantyne?utm_source=Yelp&utm_campaign=YelpwebsiteBallantyne', None, None, None, 'http://www.shippingbyeli.com', 'https://locator.chase.com/il/champaign/201-w-university-ave', 'https://www.moneytreeinc.com/branch/north-nellis', 'http://www.waggsnwhiskers.net', 'http://www.dunkindonuts.com', 'http://www.pizzapizza.ca', None, 'https://www.pelicanbaypools.com', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.desertdatarecovery.com', 'http://www.trophylv.com', None, None, 'https://www.petpalaceresort.com/locations/pet-palace-cleveland-east/', 'http://www.ecsolarscreens.com', None, 'http://www.a-techheatingandcooling.com', None, None, 'https://locations.wafflehouse.com/tx-dallas-1251', 'http://www.sharkushometowndentistry.com', '1592322462', 'https://www.cfshops.com/sherway-gardens.html', 'http://www.azbride.com/', 'http://vieroweddingdresses.com', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.taylormadelandscapes.com', 'https://www.drainkingplumbers.ca', None, 'http://stores.barnesandnoble.com/store/2778', None, None, 'http://www.holyguacamolepgh.com', None, 'http://www.paradisevalleyobgyn.com/home/', 'http://nevadaspinedoctors.com/', None, '1592322505', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592322510', None, None, 'http://www.bestpc.ca', '1592322521', 'http://moorefamilychiropractic.ca/', None, None, 'http://www.loefgrenlaw.com', '1592322531', None, 'http://besugaredlasvegas.com', 'http://littlecaesars.com/', None, 'https://www.kindercare.com/our-centers/glendale/az/000277?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=000277', 'http://www.JimmyJohns.com', 'http://www.barettocaffe.com', 'http://www.massagebook.com/biz/gary-watson-mobile-massage', 'http://www.tattooartconnexion.com', 'https://www.sephora.com/happening/stores/calgary-chinook-centre', None, None, 'https://stores.whitehouseblackmarket.com/en/white-house-black-market-biltmore-fashion-park', '1592322569', 'http://crimsonlingerie.com/', 'http://www.desertoral.com/', 'http://www.urbanherbsonline.com/', 'http://akinamotorsportz.com', 'http://www.bowmanproperties.com', 'http://www.torotaxes.com', 'http://www.alluringdesignsasalon.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'https://dealer.sprint.com/experts-choice', 'http://www.azlabsandgiants.org', 'http://dieseldoctornv.com', None, 'http://www.rubyfinchsalon.com', None, None, 'http://www.bergequicklane.com', None, 'http://www.myocarermt.com', 'http://www.bigdaddyvape.com/', 'http://www.fantasticsams.com', None, 'http://www.nba.com/raptors/community/basketball-academy/faqs', None, 'https://palmbeachtan.com/locations/OH/Boardview-Heights-Boardview-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=CLE', 'http://www.lmfoodmart.com/', 'http://www.drbishop.com', None, None, 'http://www.theforeverframe.com', 'http://livecampuscircle.com', 'http://www.homemadetemptations.com', 'https://www.kissrvrepair.com', 'http://www.ideamuseum.org/', 'http://www.dalhousieauto.ca', 'https://www.sonterraparadisevalley.com', None, None, None, 'https://www.getgocafe.com/store/details?name=robinson-cafe-getgo', None, 'http://www.primp-salon.com', 'http://www.a1partybuses.com', None, None, 'http://www.draftanddough.com', 'https://scottsdale.viliving.com?utm_campaign=webgplcdrct&utm_medium=referral&utm_source=lociq', 'http://oasisyogaspa.com', '1592322697', '1592322700', 'https://locator.chase.com/nv/las-vegas/6460-sky-pointe-dr', 'http://www.starbucks.com/store/9229/', None, 'http://www.americantitleserviceagency.com', None, None, '1592322716', 'https://www.ohiomarijuanacard.com/cleveland-office-west-side', 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'http://www.pigeonpunks.com', 'http://955themountain.iheart.com', None, None, 'http://www.vegantacos.net', 'https://www.kabobcafelv.com', 'http://www.cakedlasvegas.com', None, 'http://www.americanwashsystems.com/', 'http://www.newhongkong.ca', None, None, 'http://greencleanarizona.com', 'http://www.bartramhousebakery.com/', 'http://www.team4kids.com', None, None, None, None, 'http://comptranslv.com', None, None, 'http://sangennarofeast.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.pestcontrolcharlotte.net', 'http://www.rossstores.com', 'https://www.kohls.com/stores/nc/waxhaw-1432.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', None, 'http://www.silverstarmeats.com', 'http://www.biteyyc.com', None, 'http://www.maac.com/north-carolina/charlotte/1225-south-church?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', None, None, 'http://www.cratecook.com', '1592322816', None, 'http://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEBW', 'http://www.thebeavertoronto.com', None, 'http://islandparadisejamaicanrestaurant.com', None, 'http://www.azairservices.com/', '1592322837', 'http://www.oldnavy.com', None, 'http://www.dynamicrehabaz.com/', None, 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?language=en&STORE=12', 'http://www.ritasfranchises.com/ArcadiaTowneCenter', None, 'https://www.thompsonkane.com', 'http://www.morfurniture.com', None, '1592322865', None, None, 'http://charmeck.org/mecklenburg/county/parkandrec/parks/parksbyregion/southregion/pages/williamrdavie.aspx', 'https://www.pteglv.com/locations/pts-gold/ann-camino-al-norte/', None, 'https://locations.vitaminshoppe.com/nc/charlotte/vitamins-supplements-charlotte-nc-379.html', 'http://dawsondental.ca/our-locations/scarborough-dentist/', 'https://www.goldencorral.com/locations/2558/golden-corral-n-litchfield-drive', '1592322887', 'http://belgianchocolate.info', None, 'https://www.kaybutlerparalegalservices.com/other-practice-areas', 'https://www.korproperties.com', 'http://rethreadsfashion.com', 'https://www.cellphonerepair.com/etobicoke-on/', 'http://www.mrgreek.com', None, 'https://www.thejoint.com/nevada/las-vegas/eastern-and-richmar-36005', 'http://www.thekhanasutra.com/', 'https://www.teriyakiexperience.com/locations/markham-town-centre/', 'http://www.superpumper.com', 'http://www.gotribs.net/', 'http://www.tacomolino.com', None, 'http://www.sakanagrill.ca', 'https://www.bbvacompass.com/USA/AZ/Phoenix/21001-N-Tatum-Blvd/', None, 'https://www.lavictoriacocinamexicana.com', 'http://www.cucinatagliani.com/', 'http://hamptoninn3.hilton.com/en/hotels/ontario/hampton-inn-and-suites-by-hilton-toronto-markham-YYZMKHX/index.html?SEO_id=YELP-HP-YYZMKHX', 'http://www.surgerycenteraz.com', 'http://www.diamondmarketgrill.com', '1592322946', 'http://www.weecare4kids.com', None, 'http://www.bosspizzabar.com', 'http://www.marriott.com/hotels/travel/pitss-springhill-suites-pi', 'https://www.aps.com', None, 'http://www.newyorkfries.com', 'http://www.cyclepathmarkham.ca', 'http://www.fnb-online.com', 'https://drcooperortho.com', 'http://www.tokyosmoke.com', 'http://www.kitchenstuffplus.com', '1592322971', 'http://www.BordeauxBuilders.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.folgersubaru.com/bodyshop/collision-center.htm', '1592322983', 'http://www.solestop.com', None, 'https://outlawjeepandoffroad.com', 'http://www.klaben.com/index/dealership/dealership/3', None, None, 'http://aztitleloans.com', None, 'https://discountaaronmovers.com', 'https://www.lkpfirm.com', 'http://buonpadrepizza.com', None, 'https://www.geico.com/insurance-agents/arizona/phoenix/jack-chumadevsky/', None, 'http://sunvalleyguttering.com/', 'http://www.giggle.com/eng/storelocator/scottsdale.cfm', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.banfield.com/veterinarians/az/phoenix/pho?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://seven-star-car-detailing-ltd.business.site', None, 'https://www.musicgoround.com/locations/monroeville-pa', 'http://www.soleilvitality.com', 'http://www.marvelousfanaticsalon.com', 'http://www.gatewaydoorsaz.com', 'http://rambhadayspa.com', 'http://www.playfortmill.com', None, 'https://www.ezmini.com/self-storage-monroeville-pittsburgh-pennsylvania.aspx?utm_source=Yelp&utm_campaign=Yelp-Monroeville&utm_medium=referral', '1592323049', 'http://bigcuzs.com', None, None, 'http://www.theyardpgh.com/market-square', None, None, 'http://stlawrencecafe.com', 'https://www.smartstyle.com/en-us/locations/az/chandler/located-inside-walmart-1512-haircuts-1272.html', 'https://metrolinamed.com', 'https://haircutmenarroyocrossinglasvegasnv.com', 'http://www.banfield.com/veterinarians/nc/charlotte/bky?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.rocknrollinrock.com/', 'http://www.naeglelawfirm.com', 'http://www.mahiparkabab.com/', 'http://soaltee.ca/', 'http://www.ferraroslasvegas.com/', '1592323087', 'http://www.diamond-medical.com/', 'http://www.estateresaleconsignments.com/', 'http://www.richardpeelcontracting.com/index.html', 'http://nailsrussalon.wix.com/nailsrus', '1592323102', 'http://Www.notorioushair.ca', 'http://www.jacksonswash.com', 'http://prescottfamilydentistry.com', 'http://www.belakflowers.com', '1592323113', 'http://www.lubestop.com/Locations/Seven-Hills', None, None, 'http://burgsintheburgh.com/', 'http://www.northshoregastro.org', 'http://www.thestirstick.com/', 'http://vernlewis.com', 'https://www.supercuts.com/locations/sc/indian-land/shops-at-cross-creek-haircuts-80462.html', 'http://www.uhaul.com/Locations/Truck-Rentals-near-Tempe-AZ-85283/054252/', None, 'http://www.therichardeglyteam.com', 'http://www.honorhealthpmc.com', None, None, 'https://www.calgarycoop.com/stores/shawnessy/', 'https://www.ttc.ca/Subway/Stations/Christie/station.jsp#Schedule_', None, 'https://www.applebees.com/en/restaurants-henderson-nv/10305-s-eastern-ave-82074', 'http://www.searsauto.com', 'http://www.surpriseministorage.com', 'http://www.muscleandjoint.ca', 'http://HQrestaurant.ca', None, None, None, 'http://resultsonly.com', 'http://bamboobuddha.ca/', None, 'http://www.lvhomehunt.com', 'http://www.321zips.com/pittsburgh', None, 'https://www.lucycleveland.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216494&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.andresplasticsurgery.com/', 'http://www.chevronwithtechron.com', 'http://pghgarden.com', None, 'http://www.thebuildabrainprogram.com', 'http://eyewear-for-you.business.site', 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', 'https://www.kindercare.com/our-centers/mesa/az/300953?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=300953', None, 'http://dolcesalonandbeautybar.com', 'http://www.7-eleven.com/?yelp=29384', 'http://exclusivelyradine.com', None, 'https://escapematthews.com', None, None, None, 'https://www.dominos.com', 'http://genuinefresche.com', None, 'http://www.myStFrancisVet.com', None, None, 'http://grandepizza.com', 'http://www.alchemy360az.com/', 'https://www.dekalash.com/find-a-studio/pennsylvania/bethel-park', 'http://metricwerks.com', 'http://www.gooxymagic.com', 'http://www.drbishop.com', 'http://www.doggiestepsdogtraining.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044282956305&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.hairexcellence.net/', 'https://www.bunkersmortuary.com?utm_campaign=Yelp+Pilot&utm_medium=Website+Button&utm_source=Yelp', 'http://www.minitmaids.com', 'https://www.scottsdale-ent.com', 'https://www.hungryhowies.com/store/hungry-howies-00908?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00908&utm_content=Website_Link', 'https://www.sonoraquest.com/find-a-location/phoenix-by-appointment-only-tatum-shea/', None, 'http://www.voslasvegas.net', 'http://www.torontolightfest.com', None, 'https://carefreefloors.com', 'http://www.mobattraction.com', 'http://www.bankofamerica.com', 'http://www.hotchickentakeover.com', 'http://www.thingsremembered.com', 'http://www.homeologyaz.com', 'http://www.oculisteyewear.com', 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', None, None, None, None, 'http://www.valleycarpetrepairs.com', None, 'http://www.ecoenergyhs.ca/', 'http://ww2.cox.com/residential/arizona/home.cox?sc_id=nat_lbs_yp_res_yelp-az9_11q4', None, 'http://www.denimrevival.vegas', None, '1592323331', 'https://www.summerlinfootandankle.com', 'https://benebene-waffle-ice-cream.business.site', 'http://www.bankofamerica.com', None, None, 'http://www.bellagio.com/nightlife-diversions/baccarat-bar.aspx', None, 'https://www.parknfly.ca/Location/Toronto-Airport-Parking.aspx', 'http://SunHealth.org', None, None, None, 'http://olgasfabriclane.ca', 'http://locations.dollartree.com/sc/indian-land/5781', 'http://www.diamondhairart.com/', None, 'http://aupetitcafechezdenise.com/', 'https://meatsgonewild.com', 'http://tempeboatrentals.com', 'http://studio21danceaz.com', 'http://www.doormill.com', None, None, 'http://mcldaz.org/whitetank', 'http://www.nightclubglendale.com/#cid=yelp', 'http://www.ozprep.com', 'http://charmeck.org', None, 'http://www.petwantshenderson.com', 'http://samifruits.com/index.html#locations', None, 'http://www.modernmommyboutique.com', 'http://www.desertcanyongolf.com', 'http://www.bouncyworldlv.com', 'http://www.foodcity.com', 'http://www.bistropizzahenderson.com/', None, 'http://newmantitle.com/', None, 'http://www.taoyuanchinesemesa.com', None, 'http://www.blackrockbouldering.com', None, 'http://www.heritagefloorslasvegas.com', None, 'http://cafellini.com/st-bruno', 'http://www.go-orgocarpetcleaning.com', 'http://www.rejuvederme.com/', None, 'http://www.robertpatricksalon.com', None, 'https://www.solonsmiles.com', 'http://www.canyonfallsvegas.com', None, None, 'http://cimamedicalcenters.com', None, 'http://www.shoepalace.com?utm_source=yelp&utm_medium=yelp146', 'http://www.moneyinminutesnv.com', 'http://www.lesilveapartments.com', 'http://www.brookerockwellhair.com', 'http://www.americanmaderideshop.com', 'http://www.bankofamerica.com', 'http://lizardville.net', None, None, 'http://www.gillecetransmissions.com', None, 'https://www.maracas.ca', 'https://www.airqualityspecialistsaz.com', 'http://heelboy.com/locations/toronto-queen/', 'http://www.classicbeautyaz.com', 'https://danspoolremodeling.com', 'http://fitnessconnection.com/clubs/indian-trail/', 'http://www.heroburgers.com', None, '1592323514', 'http://HelloBrowz.com', 'http://www.architexturecle.com', 'http://www.vegasvalleymotors.com', 'http://www.bowtiesbridal.com', 'http://royalparkwine.com/', 'http://www.italpizzahouse.com/', 'http://www.valleverdevet.com', 'https://www.circlek.com/store-locator/us/rantoul/301-s-murray/m0105', 'http://www.thedailyclt.com', 'http://www.larryhparkerphoenix.com', None, 'http://www.eyebrowsrus.com', None, 'http://marriottmodules.com/charlotte_marriott_city_center/cutters_lounge', 'http://www.arizonagrandresort.com/spa/?utm_medium=enhanced-profile&utm_source=Yelp', None, 'http://www.julliesroastedcoffee.com/', 'http://www.mulayoga.ca', None, 'http://yuppiepuppysalon.com', 'https://local.safeway.com/safeway/az/goodyear/440-n-estrella-pkwy.html', 'https://www.wingstop.com/location/wingstop-1117-cleveland-oh-44128/menu', 'http://www.eastvalleymusic.com', 'https://bestgourmetpopcorn.com', 'http://www.madwoofs.com', 'http://oneloveyogaboutique.liveeditaurora.com', 'http://www.azclinicalservices.com', 'http://www.escapeartist.us', None, '1592323579', 'http://www.upmc.com/services/urgent-care/locations/pages/shadyside.aspx?curloc=&daddr=40.455928,-79.939849', 'http://salon7phx.com', 'http://www.nailsbyjoy.com/', 'http://www.freewayinsurance.com', None, 'http://www.pospisildental.com', 'http://www.lolatapas.com', '1592323600', '1592323603', 'http://www.craftstoresalon.com', 'http://www.heroburgers.com', None, 'http://www.mariecallenders.com', 'http://www.avoncleaners.com', None, 'http://www.pagoda.com', '1592323623', 'http://www.pghreptileshow.com', 'https://www.gatewayacademy.com/schools/charlotte-nc-mckee-preschool/?utm_source=yelp&utm_medium=local_listing&utm_campaign=yelp_website&cad_campaign=yelp_website', 'https://www.mcalistersdeli.com/locations/sc/rock-hill/735-addison-avenue-1066', 'http://www.cosmopolitanlasvegas.com/', 'http://www.bistromerlot.ca', 'https://www.hendels.com', 'http://signature.vze.com', 'http://theflyingpigeonphx.com', 'http://marriott.com/msnri', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=5780', 'http://www.starbucks.com/store/8054/', 'http://www.sinnersburger.com/', 'http://www.azmnh.org', 'http://www.shirazpersiancuisine.ca', '1592323660', 'https://poolstar.net', None, 'http://www.fyresite.com/?utm_source=Yelp&utm_campaign=Yelp', 'http://www.planetfitness.com/gyms/las-vegas-flamingo-nv-611?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.carsoncitysaloon.com/', 'http://www.vistamedicalgroupaz.com', None, None, 'http://www.jdcampbells.com', 'http://www.thefurrynation.com/', 'http://www.goforspa.com', None, 'https://www.sephora.com/happening/stores/toronto-eaton-centre', '1592323693', 'https://www.sanctuarybailbond.com', None, 'http://www.studio924.com/', 'http://www.mobileautoglassrepairmesa.com', 'https://www.legacygreensolutions.com', None, None, 'http://www.brazilianblowdryboutique.com', 'http://www.petlandlasvegas.com', 'http://www.lionapartmenthomes.com', None, 'http://www.royalcoffeebar.com', 'http://www.fitnessworks.com/amenities/mesa-amenities/', 'http://www.griddlecakeslv.com', None, 'http://www.haifarestaurant.com/', 'http://www.rockoasis.com/', 'http://www.madabouthairvegas.com', 'http://www.csuohio.edu', 'http://www.jeffleelandscaping.com/', None, 'http://www.jessejamesbodywellness.com', 'http://salon-glow.com', 'http://pawsitivelycleandogs.com/', 'http://www.glitterlens.com', 'http://www.lcbo.com', None, None, 'http://newks.com', None, None, 'http://www.maccosmetics.com', 'https://us.burberry.com/store-locator/united-states/nevada/grand-canal-shoppes-at-the-palazzo-las-vegas/285', None, None, 'http://www.charlottelandscapeandpatio.com', 'https://www.choicehotels.com/north-carolina/cornelius/econo-lodge-hotels/nc105/rates', 'http://www.extremepita.com', '1592323783', None, 'http://www.tlck9academy.com', 'http://www.goodyearaz.gov/communitypark', 'http://www.zinburgeraz.com/locations/phoenix/', 'http://time2tintlv.com', '1592323799', None, 'http://asukarate.com', 'http://www.lowes.com', None, 'http://www.VapeTime.ca', None, 'http://www.ancoeinspections.com', 'http://mycleaners.com/', 'http://www.omachiropractic.com', None, None, 'https://www.anytimefitness.com/gyms/781/Verona-WI-53593/?utm_source=yelp&utm_medium=local', 'http://chexgrill.com', 'http://www.falconautomotivegroup.com', 'http://collectivesalon.ca', None, 'http://www.1stchoicess.com', None, 'http://www.cafechocolade.net', 'http://www.kfc.ca/store/4980-bd-des-sources-pierrefonds', 'http://www.blaqlytetattoos.com', None, 'http://www.nandos.ca/restaurants/bay-street', 'http://www.rosenblumlawlv.com', None, '1592323855', None, 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=483', 'https://harrisburgncvet.com', None, 'http://goevergreenpest.com/', 'http://www.LoveMe.com', 'http://www.ghcapital.ca', 'http://www.diabetes.ca/get-involved/supporting-us/clothesline/', 'http://www.comforthomeappliance.com', 'http://AlibiLoungeLV.com', None, 'http://www.checkmate-mesa.cashforgold-buyers.com', None, None, None, None, '1592323887', 'http://www.apgastro.com', 'http://www.bhhskovack.com/agentsearch/agentinfo.aspx?PersonID=15474351', None, '1592323894', None, 'https://smartfixcanada.ca', 'http://www.fleetfeetsports.com', 'http://www.arbys.com', 'http://www.planetfitness.com/gyms/strongsville-oh-1550?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://www.waterstreetgrill.net/', None, None, None, 'https://www.anytimefitness.com/gyms/3902/Bethel-Park-PA-15102/?utm_source=yelp&utm_medium=local', 'https://www.brandonscomics.com', 'http://shesc.asu.edu/dvpp', 'http://rbakery.ca', '1592323925', 'http://www.my931.com', 'http://www.bwsweetsbakery.com', 'http://www.revpizza.com/', 'http://www.addisononeglinton.com/', 'http://www.tcby.com', 'https://xactcrete.com', None, 'https://roc.az.gov', '1592323952', 'http://www.joann.com', 'https://locations.wendys.com/canada/on/oakville/2304-royal-windsor-drive', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.786halalrestaurant.com/', 'http://www.soultosoulaz.com', 'http://classicpoolserviceaz.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044282956800&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.dominos.com', 'http://www.lapetite.com/your-local-school/las-vegas-nv-7300/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://www.thefarmgolfcourse.com/', 'http://www.burritoboyz.ca', 'http://www.ispa7.com', 'http://vietnamesenoodleairdrie.com/', '1592323989', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://paintingandvino.com', 'http://www.snapfitness.com/gyms/mississauga-on-l5k0a1/1404', 'https://americanrawfitness.com', 'http://stashpadvintage.com', None, 'https://www.rackroomshoes.com/?utm_source=Yelp%20&utm_medium=localsem%20&utm_campaign=20170330_RRS%20&utm_content=webtraffic', 'http://silverstatelandscaping.com', 'https://www.adobemassage.com', None, 'http://www.greatclips.com', 'http://www.fastfix.com/', 'http://www.lcbo.com/webapp/wcs/stores/servlet/AjaxStoreLocatorDisplayView?catalogId=10001&langId=-1&orderId=&storeId=10151&storeNum=10611&fromPage=StoreDetails', None, None, 'http://www.kennyross.com/', 'https://www.skyharbor.com/Museum', 'http://datingincharlotte.com', None, 'http://c3arms.com', 'http://www.winghouseandsportsbar.com/', None, 'https://www.angrycrabshack.com/litchfield-rd-goodyear-az/', None, 'https://www.chick-fil-a.com/arboretum', 'http://www.peterpiperpizza.com/', 'http://www.battlegroundsportsaz.com/', 'http://papajohns.com', 'https://www.azgunslinger.com', 'http://www.suntouch.ca', 'https://friendlydentalgroup.com/south-park-dentists/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Yelp%20Ads', None, 'http://www.azmetrohauling.com', None, None, None, 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', None, 'http://www.gymboree.com', 'http://bulwarkalarm.com', 'https://www.monaco-pittsburgh.com/?utm_source=yelp.com&utm_medium=business+listing&utm_campaign=profile+url', 'http://thebrowladyusa.com', 'http://www.montanas.ca', 'http://adcstreetsboro.com', 'http://theschnitzerlawfirm.com', 'http://www.serranosaz.com/', 'http://www.nextcare.com/locations/az/phoenix-thomas/?utm_source=Yelp&utm_medium=Local&utm_campaign=phoenix_thomas', None, 'http://www.printwise.com/', '1592324114', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/32331+North+Scottsdale+Road-Scottsdale-AZ-85262/storeid=7839?cid=ps_ylp_2020', 'http://www.malleys.com', 'http://www.clevelandoktoberfest.com', 'http://www.flooroneaz.com', 'http://www.markhameventcentre.com', 'http://www.steakenburger.com', None, 'https://www.caferio.com/locations/eastern', 'http://myenso.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://stitchit.co/store_locator/sheridan-centre/', None, 'http://landrovercalgary.com', None, 'https://milios.com', None, 'http://westlakelaserwash.com', 'http://www.sporkpit.com', 'https://deciem.com', 'http://www.shillelaghspub.com/signalhill/', 'http://www.irepairswireless.com', 'https://www.walgreens.com/locator/walgreens-6649+morrison+blvd-charlotte-nc-28211/id=1376', 'http://www.motorcycletraining.com/', 'http://www.marswholesale.com', 'https://smiledirectclub.com/smileshops/phoenix-arcadia/?utm_campaign=yelppaid&utm_medium=cpc&utm_source=yelp&utm_content=phoenix', 'https://laflame.business.site', 'http://www.industriousoffice.com/locations/charlotte?utm_source=yelp&utm_medium=cpc&utm_campaign=lp&utm_content=website&utm_term=a', 'http://m.fairystouchcleaning.com/', None, 'http://www.shell.us', 'http://griffisresidential.com/properties/summerlin-south/', None, None, 'http://www.gttdogs.com', 'http://www.bellautoupholstery.com', 'http://lamin-8.ca/', 'http://www.ritasice.com', 'http://locations.tccrocks.com/az/glendale/20211-n-67th-ave.html', 'https://www.walmart.com/store/5403/urbana-il/details', 'http://scottsdalemuffler.com', 'http://www.mikesautobodypgh.com', None, 'http://www.53.com', None, None, 'https://www.elementfleet.com', 'http://www.penn-station.com', 'https://www.hendrickcollision.com/Hendrick-Luxury-Collision-Center-Charlotte-NC.html?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, 'http://www.motorwerkes.com', 'https://lawnlove.com/phoenix-lawn-care?utm_medium=ListingTraffic&utm_source=Yelp', '1592324244', None, 'http://www.sevillefamilydentistry.com', '1592324251', 'http://www.azbrew.com/', 'http://www.debbiebakersellsaz.com', 'http://www.advanceopticians.com', 'http://www.gabesstores.com', 'http://birdandhike.com/Hike/LAME/Bluff/_Bluff.htm', 'https://www.watersidedentalcare.com', '1592324270', None, None, None, 'http://bobbyq.net', None, 'http://www.empire.edu/cosmetology-schools/arizona/avondale-goodyear&v=yelp', 'http://www.willowbrookcarwash.com/wb2/', 'https://www.kevinsdeli.com', 'http://dulcealterations.com', 'https://www.carvana.com', None, None, 'http://www.sesameinncarefree.com/', None, 'http://www.desertjewelobgyn.com', 'http://www.townsquaredental.com/', None, 'http://www.rentacarphoenix.com', '1592324317', 'http://www.superpumper.com', 'http://www.vividsalonllc.com', 'http://www.shopnsavefood.com', 'https://www.sprint.com/apps/save50percent/index.html', 'http://www.bedrocklasvegas.com', None, 'https://harmonyrealty.managebuilding.com/Resident/PublicPages/Home.aspx?ReturnUrl=%2fResident%2fdefault.aspx', 'https://www.levinfurniture.com/furniture-store/oh/middleburg-heights/16960-sprague-road', 'http://www.metromovement.com', None, 'http://denaliservicesaz.com', 'https://jandsdiesel.com', None, '1592324351', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', '1592324357', 'http://www.unioncabaz.com', 'http://alphx.org/thrift-shop', '1592324365', 'http://www.tjscollision.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://Uppercervicalchiropracticlv.com', 'http://www.wisconsinhistory.org/', 'http://stevesautoservicemurrysville.com', 'http://www.fredsbarandgrill.ca/', 'http://www.americanstarsecurity.com', 'http://suntancity.com/tanning-salon-locations/wisconsin-madison-wi-madison-east-towne-way/', '1592324393', 'https://silvaprofessional.wixsite.com/mysite', None, 'https://www.oakbankonline.com', 'http://www.lakenormanobgyn.com', 'http://www.bedazzledbridal.com', None, 'http://www.sweetiescandy.com', 'http://www.kadampa.ca', 'https://pokitrition.com/location/', 'https://www.chick-fil-a.com/arboretum', 'https://stores.petco.com/az/glendale/pet-supplies-glendale-az-1108.html', 'http://www.orbissolutionsinc.com', 'https://www.solevowellness.com', 'www.us.travelex.com', 'http://www.sunnails.net', 'https://megafurnitureusa.com', 'https://www.opticaleffectslv.com', 'https://totalhairrehab.com', 'https://huajia-rice-noodle.business.site', None, 'https://www.ifixicell.com', 'http://www.paradisecarcare.com', None, None, 'http://eyeinstituteaz.com', 'http://www.quiktrip.com', 'http://www.nakamori.ca', None, None, None, 'http://www.diefplumbco.com', 'http://restoremaster.biz', 'http://arizonafertility.com/', 'http://sammys-auto-service.business.site', 'http://www.expertmechanix.com', 'http://scottsdalecc.edu', 'http://bluediamondah.wixsite.com/blue-diamond-ah', None, 'https://www.dollartree.com', 'https://local.fedex.com/oh/mentor/office-1237/', None, 'https://local.firestonecompleteautocare.com/arizona/phoenix/1141-e-bell-rd', 'https://www.redlobster.com/locations/list/nc/gastonia/200-n-new-hope-road', 'http://www.bretrunion.com', 'http://www.livnorthscottsdale.com/', None, 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://www.themowertech.com/', 'http://www.thespeakeasyalehouse.com', 'http://www.justbsalon.ca', 'http://www.sciatica.com', 'http://www.elevationburger.com/', 'http://www.theglamparlor.com', 'http://www.centralebergham.com/', 'https://www.cox.com/local/residential/stores/oh/parma/12221-plaza-drive?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q4', None, None, 'http://www.leevalley.com', 'http://www.futureforwildlife.org', None, 'http://eastridgemall.net/', 'http://www.yogaforlifecharlotte.com/', 'http://www.uwbookstore.com', 'https://www.sephora.com/happening/stores/champaign', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://www.villamontessori.com', 'http://www.bumpyscafe.com/', 'http://hudsonscanadaspub.com/location/crowfoot', 'http://www.byblosbakery.com/', 'http://www.sorensonpediatricdentistry.com', 'http://www.captainstreasures.biz', 'http://www.ashlarpainting.ca', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'http://www.honeybeebakerymedina.com', 'http://www.freshandeasy.com', None, 'https://www.killarneycat.com', '1592324589', 'http://www.sassysbarandgrille.com', 'http://www.zupadi.com', '1592324598', 'http://www.delacrepe.com', 'http://www.culvers.com/restaurants/champaign-marketview', 'http://chachis.ca', 'http://expressfactoryoutlet.com', 'http://www.pierogimarket.com', 'http://www.fiestahendersonlasvegas.com/dining/dennys/?utm_source=YELP&utm_medium=SOCIAL&utm_term=FH&utm_content=FH-PROPERTIES&utm_campaign=FH-YELP', 'http://www.tuckerstennis.com/', 'http://www.limelightwork.com', None, 'http://www.Bikinibeansespresso.com', 'http://www.saucepizzaandwine.com/locations/phoenix', '1592324626', 'http://childtherapyaz.com', None, None, 'https://www.applebees.com/en/restaurants-streetsboro-oh/1200-state-rt-303-96096', '1592324639', None, '1592324645', 'http://www.wingstop.com/default.aspx', 'http://expressionsboutiqueaz.com', None, None, 'http://www.edgessalon.com', 'https://www.hobbyaction.net', 'http://www.maac.com/south-carolina/charleston/colonial-grand-at-commerce-park?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://www.sushiherolv.com', '1592324667', 'http://www.tlsinghlaw.com', None, None, 'http://www.reids.com', 'http://www.visitsealife.com/charlotte-concord', 'http://www.wrongful-dismissal.com', 'http://www.cplpropertiesonline.com', '1592324687', 'http://www.torontocoffeecompany.com/Home.html', 'https://lmullins1225.wixsite.com/VegasTailorsCleaners', None, None, 'http://www.bojangles.com', 'https://www.walgreens.com/locator/walgreens-1745+e+southern+ave-tempe-az-85282/id=1197', 'https://weingrowwellness.com', None, None, 'http://madaboutdance.com/', 'http://www.debeckerinvestigations.com', 'https://www.proudfoot-services.com', None, None, 'https://www.earthfare.com/our-stores/solon', 'http://www.knightsinn.com/hotels/hotel-overview?hotel_id=47653&tel=18884240138&wid=fe:kg:20160215:yl:pp:kg:47653', '1592324720', 'http://www.calpool.com/', None, None, 'http://charlotte.littlenestphoto.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.globalintlcanada.com', None, 'http://www.ec-orthotics.com', None, None, None, 'http://pacificelectriclv.com/', 'http://www.thecuckoosnest.com', 'http://www.upmc.com/locations/hospitals/st-margaret/Pages/default.aspx', 'http://affiliatedinternalmedicine.com', None, None, 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', None, 'https://www.applebees.com/en/restaurants-avon-oh/35916-detroit-road-99047', 'http://www.renovationpiano.com', 'https://www.kitandace.com/ca/en/locations/Toronto-Queen%20St', 'http://www.platosclosetmadisoneast.com', 'http://www.bbwindowcleaning.com', 'http://www.dunkindonuts.com', 'http://www.triplebfarms.com', 'http://boltontoyota.ca', 'https://www.shulas.com/shulas-steak-house/chandler-az/#1491407149596-ee25d46a-e7e6', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.marshallsonline.com', None, 'http://www.shawarmahut1.com', None, 'http://www.finechiropractic.com/', 'https://www.hilton.com/en/hotels/msndtdt-doubletree-madison-downtown/?SEO_id=YELP-DT-MSNDTDT', 'http://pubrocklive.com/', '1592324809', 'http://www.umbra.com', 'http://www.AudreyMendozaMakeup.com', 'http://www.yelp.com/events/scottsdale-yelp-shops-local-holiday-shopping-crawl', 'http://www.quiktrip.com', 'http://www.oakvilleplace.com', 'http://www.gcsflooringcompany.com', 'https://lawofficeofkarenhross.com', 'http://www.redpegasus.ca/', None, 'http://islandcomfortlv.com', 'http://www.nomoreleash.com', 'http://www.austinelectricservices.com/home', 'https://www.orangetheory.com/en-us/locations/ohio/akron/34-north-hawkins-avenue-suite-305/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, 'http://www.shirazrestaurant.ca/index.php?option=com_chronocontact&Itemid=6', None, 'https://www.findlayacura.com', 'http://www.wilsonsisters.com', None, 'https://www.burksbbq.com', 'http://www.akafitness.com', 'http://timdeibert.com/', None, 'http://www.hollywoodcoffeeaz.com', None, 'https://www.mark-taylor.com/apartments/az/chandler/avant-fashion-center/?utm_source=Yelp&utm_medium=reputation&utm_campaign=main', 'http://www.prioritytow.com', 'http://www.celebrityskinstudio.com', 'http://www.autotechsquad.com', 'https://www.novahomeloans.com/arrowhead-office/', 'https://myhoneybakedstore.com/lasvegas/1102', 'https://www.bankofamerica.com/', 'http://andreasbakery635.com/', None, None, None, 'http://www.econrads.com', 'https://www.camdenliving.com/phoenix-az-apartments/camden-north-end', 'http://www.sweetrepublic.com', 'http://paradisebakery.com', 'http://alcoparking.com/lot-garage/west-general-robinson-street-garage/', None, 'https://www.jbsed.com', None, 'http://bikedraz.com', 'https://www.medexpress.com', 'http://www.lindsaywynneboudoir.com', 'http://www.paychex.com', 'http://www.urbanbarn.com/store-locator/queen+west.do', 'http://www.bigbuddhaaz.com', 'http://www.district8beer.com', 'https://www.nhpinevilleprimarycare.org', 'http://www.angelosrestaurants.com', 'http://www.paradiselaserbotox.ca', 'https://dealer.sprint.com/connectivity-source/find-a-store/256933-scottsdale-az-85250', 'http://www.chasethetrainer.com', 'http://www.dkenvy.com/', None, 'http://www.bridalbylaurieann.com', 'http://www.eastsidecannery.com/dining/casa-cocina', None, 'http://www.downtownchrysler.ca', 'http://www.fuziongroup.ca', 'http://www.todaystiffany.net', None, None, None, 'http://www.videogamerepairtoronto.ca/', None, None, None, 'https://www.caesars.com/caesars-palace/shows/jerry-seinfeld#.XMLEGzAzaCg', None, 'http://ypxr.ca', 'http://www.cowboysnightclub.com', 'http://www.thefreshmarket.com/', 'https://local.safeway.com/safeway/az/phoenix/3132-e-camelback-rd.html', None, 'http://www.mastertech-autoservice.com', None, None, 'http://www.rockychoc.com/location/first-canadian-place/', 'http://www.heritagebakeryanddeli.ca', 'http://www.garagedoormore.com', 'http://westfieldcomics.com', 'http://www.xtremetreeservices.com/', 'http://www.blackmoonlounge.com', None, 'http://www.holidayinn.com/hotels/us/en/pittsburgh/pitav/hoteldetail', 'http://www.mazengames.com', None, 'https://www.wildwingrestaurants.com/location/thornhill/', 'http://www.animalvaccinationservice.com', 'https://dutchbros.com/?utm_source=phoenix&utm_medium=yelp&utm_campaign=website_phoenix', None, 'http://www.hashhouseagogo.com', 'http://www.mayfairclubs.com/', 'http://www.lakewoodurgentcare.org', None, 'http://www.sugotrattoria.ca', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.SmokersLV.com', None, 'http://www.epiclandscape.net', 'http://www.papajohns.com/', 'http://www.hyundaisouthcharlotte.com/?utm_source=yelp&utm_medium=referral&utm_campaign=local-citations', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd', 'http://www.micasatoronto.com/', None, None, None, 'https://www.bashas.com/stores/bashas-supermarket-waddell-reems/', 'http://www.myhealthymeal.com', 'http://www.exporail.org', 'https://universalgaragedoorsllc.com', None, 'http://www.holdengracehighpark.com', None, 'https://lanasnailsandspacavecreek.com', 'http://lvcarswest.com', None, 'http://winghartburgers.com/', None, None, 'http://www.freshii.com', 'http://www.littlecaesars.com/', 'https://www.kinnearlock.ca', 'http://www.herpersonaltraining.com', 'https://www.mypillow.com', 'http://palms.com/send-noodles.html?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', None, 'http://www.roma1090.com', None, 'http://www.FlashFurnace.com', 'https://elpatrontires.com', None, None, None, 'http://www.blackhairsalonclevelandohio.com', 'http://vanrijkestatejewellers.com/', '1592325159', 'http://faganpainting.com', 'https://www.petsuppliesplus.com/Store/AZ/Scottsdale/North-Scottsdale/4190', 'http://www.pizzapatron.com', None, 'http://www.myrotiplace.com', 'http://www.toronto.ca/special_events/thursdays/2011/index.htm', None, 'https://eavensonelectric.com', None, None, None, 'http://www.berridgenursery.com/', None, 'http://www.lovechix.ca', None, 'http://www.pankowconstruction.com', 'https://www.thewireguyelectric.com', 'https://www.calgarycoop.com/stores/shawnessy/', 'https://prestigedrycleaning.wixsite.com/prestigedrycleaning', 'http://www.medinasteakhouse.net', 'https://www.gillespieapts.com/carriage-lane', None, 'http://marlasfashions.com', 'https://www.harveys.ca', 'http://www.bizzybeeplaycentre.ca/', 'https://getgreaterlifechiropractic.com', 'http://chase.com', 'http://brooksorthodontics.com', 'http://www.woodbridgeribfest.com/', 'http://www.lucidmoto.com', 'http://www.fransrestaurant.com', 'http://www.splace247.com', None, 'http://www.coppercreek.ca', 'http://ez-moneypawn.com/', '1592325250', None, 'http://www.perfectthreading.com', 'http://www.chocolateswan.com', 'https://www.brennanscatering.com', None, None, None, 'http://www.Thekitchen-Brunch.com', None, 'https://m.certifiedcs.com', None, 'http://www.cityofhenderson.com', 'https://petmedic.vet/hospitals/seven-hills-pet-hospital/', None, 'http://www.amyscafe.com/', 'http://beautifulazrvrepairllc.com', 'http://www.par2golf.com', 'http://www.reddragontattooparlour.com', 'http://www.bluehorse.blue', '1592325298', 'http://www.rdslawncare.com', None, 'http://www.terago.ca', 'http://www.fastframe109.com', 'https://azbodiesinbalance.com', 'https://www.cadence-academy.com/schools/charlotte-nc-northlake-preschool/?utm_source=yelp&utm_medium=local_listing&utm_campaign=yelp_website&cad_campaign=yelp_website', 'http://www.starloancenters.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZSI', 'https://www.oneazcu.com/about/locations/north-scottsdale-branch/', '1592325325', 'http://www.starbucks.com/store/9298/', None, 'http://www.meganlacydoeshair.com', 'https://hellolaserspa.com', 'http://ventcleaningvegas.com', None, None, 'http://www.opexfit.com', 'http://kiveralaserspa.com', 'http://www.miyaki.ca/', 'http://www.availvapor.com', 'http://www.cras.edu', 'http://www.aspirelasvegas.com', 'http://cultivatecoffee.org', 'http://thelocalbarberandshop.com', 'http://lightcafe.ca', 'http://www.revivalprintco.com/', None, 'http://99only.com/store/Las-Vegas---Beltway/', 'http://www.funkfit.com', None, None, None, None, 'https://www.choicetransmission.com', 'http://www.oldfaithfulshop.com/', 'https://snootypets.com', 'https://queencityballroom.com', 'http://www.accidentawardslasvegas.com', 'http://www.allaboutdogsllc.com', 'http://www.canyonfallsvegas.com', 'http://www.verdemaison.com', None, '1592325426', None, 'http://www.drarmitysimon.com/', 'https://rainbowpoolplasterlv.com', 'https://stores.hallmark.com/az/tempe/dianes-hallmark-shop-tempe-az-63363.html', 'http://www.cleatswings.com/', 'http://www.Alliancemhs.com', 'http://www.laurenmullanrealty.com', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', '1592325448', '1592325451', 'http://www.robinsontownshipsmiles.com/', 'http://www.jacks-tax.com', 'http://nevadarepairs.com', None, None, 'http://www.yscanadianlaser.ca', '1592325472', 'https://www.smilesatisfaction.com', 'http://www.theclotherie.com/', 'http://perfect10nailandspa.com', 'https://druxys.com/location/2-st-clair-ave-colonia-place/', 'http://www.gerrardpizza.com', None, 'http://wrichaircooling.com', 'http://www.carapowersports.com', 'http://www.mysticpointedental.com/', None, 'http://www.blackstarrfrost.com', 'http://www.tonysautoservicecenter.com/', 'http://brossard.paologattuso.com', '1592325510', 'http://www.theresortatsummerlin.com', 'http://www.optimyze.me', 'http://www.bulldogbattery.com/', 'http://www.friendlygreekdanforth.com/', 'http://www.rhythmicsouls.com/', 'https://www.petsuppliesplus.com/Store/OH/Fairview-Park/Fairview-Park/27?utm_source=Yelp&utm_medium=Store-Page%C3%8A', '1592325530', 'https://www.crownnailsandspa.com', '1592325536', None, None, 'http://www.yellowroomphoto.com', 'http://www.gillsgrounds.com', 'http://www.wm.com', 'http://libertytreeexpertsaz.com', 'https://phillips-landscaping-services.business.site', 'http://www.dickscabaret.com', 'http://www.alleghenycounty.us/parks/hwfac.aspx', None, 'http://7eleven.ca/store-locator/36704', 'https://www.walmart.ca/en/stores-near-me/westbrook-store-3009', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB085', 'http://www.tantemays.com/index.html', 'http://www.jaderiverbuffet.com', None, None, 'https://www.jiffylube.com/locations/az/peoria/659', 'http://teamintegrityvegas.com', 'http://www.ingoodhandsnc.com', 'https://www.thecamptc.com/location-midphoenix.php', None, '1592325596', 'https://nocovernightclubs.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://insomniacookies.com/locations/store/1195', 'http://www.beefobradys.com', None, 'http://www.baskinrobbins.com', 'http://www.futureshop.ca/', 'http://www.marcos.com/locations/oh/lorain/leavitt-rd?s=true', None, 'http://alibabas.ca', 'http://www.myfreedomsmokes.com', 'https://herbalnailschandler.com', 'http://myleesbridal.com', 'http://Reedchiropractic.com', 'http://www.nvpita.com', '1592325637', None, 'https://www.thewillowsrestaurantandbar.com', None, 'http://48thstate.com', 'http://www.familylifecenters.org', None, 'http://www.galleriasm.com/branch/store/ym', None, 'http://www.freshii.com', 'http://dozenbakeshop.com/', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://www.onezotapioca.com', 'http://www.hilldale.com/', '1592325669', 'http://www.empoweredk9.com', 'https://www.lookstylesociety.com/gentlemens-quarters/', None, 'http://www.TruePilatesLasVegas.com', None, 'http://www.gemmasfashion.com', 'http://www.ironmanpoolfence.com', None, 'http://www.muddypawsintheguild.ca/', 'http://www.paulsacehardware.com', None, 'http://www.redztransportdivision.com', '1592325703', 'http://www.elitetax.net', 'http://rollingtones.info', 'http://www.helpinghandhaulers.com', None, 'https://treetoptrekking.com/parks/brampton/', None, 'http://www.thephxstudio.com', 'https://ongortho.com', None, None, None, 'http://www.surfacesaversonline.com/', 'http://www.superior-tire.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.pizzahut.com/', 'http://www.houseofleng.com', 'https://www.lowkeypianobar.com', 'http://www.exquisidance.com/', 'http://www.autonationchevroletgilbert.com', 'http://www.normantireandauto.com', 'http://www.caymanpoolspa.com', None, None, None, None, 'https://www.bootbarn.com', None, 'http://villagepubcasino.com', None, 'http://nevadahand.org', 'http://www.glutenfreebakeree.com', None, 'http://www.globalpetfoodstoronto.ca/locations/beaches/', 'http://www.ThePassion8.com', 'https://www.familydoctorsbc.com', '1592325802', None, 'http://www.pureblissfit.com', None, 'http://www.clearsightohio.com', '1592325816', 'http://www.macumbers.com', None, 'http://hackeryou.com', 'http://www.yorkdaledufferinmazda.ca/', 'http://www.sharpgroupco.com', 'https://trillphx.com', 'http://locations.arbys.com/us/nv/north-las-vegas/1465-w-craig-rd.html', 'http://www.carlsjr.com', '1592325839', 'http://www.belsitoplumbing.com', None, None, 'https://cprsociety.org/take-a-class/', 'http://www.vfoutlet.com', 'http://www.jenjinkensphotos.com', 'http://www.learnnplayaz.com', 'https://www.charlotteradiology.com/location/ballantyne-breast-center/', None, 'http://joiaristorante.com/newmarket/', 'http://www.mchalesirishpub.com', 'http://www.clevelandbeerfest.com', None, 'http://www.hjacks.com', 'https://teamtntfitness.com', 'http://puresushibar.com/', 'http://www.thebluestonebistro.com', '1592325884', None, 'http://elitenailsgilbert.com/', 'http://www.a-oklocksmiths.com', 'http://www.rainbowcottoncandy.com', 'http://www.mmmuffins.com', None, 'http://www.starwoodhotels.com/fourpoints/property/overview/index.html?propertyID=1256&EM=YELP_4P_1256_NAD', 'https://www.carmax.com/stores/7157?adcode=YLP7157&utm_campaign=LG_AFF&utm_source=LG_AFF_YLP&utm_medium=local&utm_content=shop', None, None, 'http://www.cpmadisonhotel.com', 'http://qspa.ca', 'https://www.associated-dental.com/practices/associated-dental-care-gilbert', None, 'http://www.mixedpet.com', 'http://www.ncbiryani.com/', None, 'https://www.take5oilchange.com/locations/nc/charlotte-27/', 'https://www.bobacrazeaz.com', 'http://www.thebestdetail.com', None, 'https://www.walgreens.com/locator/walgreens-5220+highway+557-lake+wylie-sc-29710/id=10838', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.buathai.ca/', None, 'https://www.h2osushiizakaya.com', 'http://www.kimchikorea.ca/', None, 'https://www.choicehotels.com/nevada/las-vegas/comfort-inn-hotels/nv059/rates', 'http://www.calvinklein.com', 'https://www.walmart.com/store/1532/glendale-az/whats-new', '1592326519', 'http://www.redrockmedical.com', 'http://gametimefun.com/mississauga/', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', 'http://estiboutique.com', 'http://www.fullyloadeddeliveries.com', None, 'http://www.desertpalmsemu.com', 'http://longbowdentalcare.com', None, 'http://walmart.com/', 'http://hazeltonlanes.com/', 'http://www.poshburgerbistro.com/', '1592326551', 'https://www.menswearhouse.com/store-locator/2504?utm_source=yelp&utm_medium=listing&utm_content=2504&utm_campaign=AZ', 'http://janjewelers.com', None, 'http://www.timhortons.com', None, 'http://www.danceology.org/', 'http://www.troikavodkaboutique.com', 'http://sosharpbarbershopaz.com', 'https://www.grilladesfarhat.com', 'http://www.lakewoodupholstery.com', '1592326574', 'http://www.phxeyecare.com', None, None, 'http://www.kalamazoovaporshop.com', '1592326585', 'http://tinytlc5.wix.com/tiny-tlc', None, 'http://lasvegasflowerpetal.com', 'http://www.smilecharlotte.com', 'http://www.goldenjadeinc.com', 'https://wavescoffee.com/our-stores/springborough', None, None, None, 'http://www.deeplyrootedaz.com/', None, '1592327011', 'http://www.granowskasbakery.com', None, 'http://www.starbucks.com/store/14175/', 'http://www.wdclv.org', None, 'http://arizonacorporatecoach.com', 'http://www.meinmanphx.com', 'http://www.needlesupply.com', 'http://www.nellacucina.ca/', 'https://jonathanandolivia.com', 'https://www.exoticaskincares.com', None, 'http://www.thedarlingmansion.com', None, None, 'http://www.ModernManorStore.com', None, None, 'http://www.homegoods.com/tjx/store.aspx?id=496', 'http://savethefamily.org/thrift-store-2', None, 'http://www.worldwiderv.com', 'https://kidstoptoys.com', 'http://www.probatelawyerlasvegas.com/', None, 'http://www.escapedvegas.com', 'https://www.stewartaz.com/', None, 'http://www.billscustom.com', None, 'http://www.wellsfargo.com', 'http://www.winghouseandsportsbar.com/', 'http://Studiockbeachwood.com', 'http://gabbys.ca', 'http://www.pizzajoes.com/leetsdale', 'http://www.kingdavidpizza.ca/', None, 'http://www.gamersinnaz.com', None, 'http://www.timhortons.com', None, 'http://www.lakewilcoxbrewing.com', 'http://www.gatewayexecutivesuites.com', '1592327117', None, '1592327120', None, None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://loveandphoto.com', 'http://www.boffwallbeds.ca', 'http://www.chiamrestaurant.com/', 'http://Thai-on-Demand.com', None, 'http://www.cafe8az.com', 'http://www.cobsbread.com', 'https://www.honorhealth.com/locations/specialty-care/honorhealth-sleep-disorder-center?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-sleep-disorder-center', 'http://www.badgerstatetowingllc.com', '1592327155', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://montlackrealty.com', 'https://www.enterprise.com/en/car-rental/locations/us/il/champaign-s-neil-st-6202.html?mcid=iyp:8368400', '1592327165', 'http://southernhillsah.com', 'https://www.gadventures.com', None, 'http://www.madisonmusic.com', None, 'http://knollwoodcemetery.net', None, None, None, None, 'https://arrowheadhealth.com', 'https://fox-steven-g-phd.business.site', 'http://www.lococantinalv.com', 'https://www.choicehotels.com/arizona/mesa/sleep-inn-hotels/az022/rates', None, 'http://www.topdocsaz.com', None, 'http://www.bentrestaurant.com/', 'http://www.barbsbridalboutique.com/', 'http://www.catchrestaurant.ca', 'http://www.jackrabbitnurseryaz.com', 'http://www.billskeyshop.com', 'http://www.hqslv.com', None, 'https://www.walkingonacloud.com/walking-on-a-cloud-yonge-&-richmond/', 'https://www.zoup.com', 'http://bbcphx.org', 'http://canyonridgeoms.com', 'http://www.blackumbrellagallery.com', None, 'http://www.peoriahealthsolutions.com', 'http://elsombrero.ca/', 'http://moxie-girl.com', 'http://www.starbucks.ca', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'https://landrovermetrowest.ca', None, 'https://www.jerseymikes.com/7006', 'http://www.roppongisushibar.com', 'http://pepesbbqaz.com', 'http://imappliancerepair.ca', 'http://itechwireless.ca', 'http://www.co-te-rie.com', 'http://www.desertcomputersolutions.net', '1592327276', 'http://www.villageinn.com/locations/110695', None, 'http://www.dentistingilbert.com', 'http://www.vintageouslife.com', '1592327290', None, None, None, None, 'http://www.hawthornecafe.ca/', 'http://www.aztaxservice.com', None, None, 'https://www.interdent.com/gentle-dental/locations/nv/las-vegas/3016-w-charleston-blvd-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.suburbanglass.ca', 'http://www.urbangrub.ca', None, 'http://www.krispykreme.com', 'http://www.dunkindonuts.com', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=244', None, None, None, 'http://www.sheilasdrapery.com', None, None, None, 'https://www.cash1loans.com/locations/arizona/phoenix-thomas.aspx', 'http://tiara.ie/', None, None, 'http://lacasatequila.net/index.html', 'http://www.picknsave.com', 'http://www.durhamlawfirm.com', 'http://www.basesloadedlv.com', None, None, 'http://www.thesmithohio.com', None, None, 'http://www.theflatsatpeoria.com/', 'http://www.mullinslaw.net', 'http://samsxpresscarwash.com/indianland', None, 'http://www.cqlys.com', None, None, None, 'https://www.marriott.com/hotels/hotel-information/restaurant/details/phxwh-w-scottsdale/6500593', None, 'http://www.quiznos.com', 'https://www.walmart.com/store/1863/willowick-oh/whats-new', None, None, None, 'http://onsiteautoalarms.com/', 'http://www.greatergoodsco.ca', None, 'http://www.actionvacuum.com', 'http://www.canopyblue.ca/', 'http://www.bosstransaz.com/home.html', 'https://www.avanagilbert.com', 'http://bmv.ohio.gov/28.stm', 'http://www.straightonchurch.com', 'https://nailclinic.com', 'http://winghartburgers.com/', '1592327476', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89015/601-in-henderson/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-601&utm_content=website-link&howheard=IYE', 'http://www.furnitureroyal.biz/', 'http://www.thecamptc.com/location-arcadia', 'http://www.shoppetal.com', 'http://www.alternativeautorepair.net', '1592327494', None, 'http://www.aztreedoctor.com/contactUs.html', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://mortgage360.ca', 'https://locations.wendys.com/united-states/az/chandler/1045-s.-arizona-ave', None, None, 'http://Dragonflypilates.Com/', 'http://www.parknfly.ca/', 'http://www.teashop168.ca/', None, 'https://www.umcsn.com/Quick-Cares/Quick-Cares-Index.aspx?intMenuID=100&intPageID=112', 'http://www.pittsburghjuicecompany.com/', 'http://mtnviewglass.com', '1592327543', 'http://boarandbarrel.com', None, 'http://www.hongkonggardenrestaurant.ca', None, 'http://www.kenmarciel.com/math-tutor', 'https://www.homedepot.com/l/Maple-Heights/OH/Maple-Heights/44137/3804?cm_mmc=seo-yelp&', None, 'http://knockout-fitness.com/locations/surprise', 'http://www.alsfishandchicken.com', 'http://www.poshpupspa.com', 'https://www.mercedes-benz-brampton.ca', 'https://locations.mrtire.com/nj/lakewood/2023-madison-avenue?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.superlativeremodeling.com', 'http://www.casadolcespa.com/', 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', 'http://www.herfathers.ca', 'http://www.valleypediatricdentists.com', '1592327602', 'http://gvlas.com', 'http://www.popphysique.com/toronto/', 'http://boxbros.com', 'https://www.thetenspot.com/beaches', 'https://www.thetoastingcompany.com', None, 'http://www.reflectionsatredmountain.com', None, None, 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'https://www.orangetheory.com/en-us/locations/north-carolina/charlotte/8402-park-road/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, 'http://www.bk.com', None, None, 'https://www.orangetheory.com/en-us/locations/north-carolina/charlotte/14825-ballantyne-village-way-suite-a180/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, None, None, None, 'http://www.allaboutacme.com', None, 'http://www.foreign-traffic.com', 'http://www.luckybamboo.ca', 'http://storelocator.pepboys.com/pepboys/stores/las_vegas/east_charleston/00685', None, 'http://davecurranlive.com/', None, 'http://www.keepcalmwaxon.com/', None, 'http://www.birrieriajalisco.com/', None, None, 'https://www.rubytuesday.com/', 'http://www.regovichcatering.com', None, None, 'http://www.blm.gov/az/st/en/prog/recreation/hiking/quartz.html', 'http://www.juneslegal.com', 'http://www.clebagelco.com', 'https://www.visioncenterslv.com/summerlin/', 'http://partyzams.wix.com/singingtelegrams', 'http://www.greencrush.com', 'http://aldi.us/index_ENU_HTML.htm', None, 'https://herbalnailslaveen.com', 'http://www.bo-pelouse.com', 'https://www.medexpress.com', 'http://www.theyogawhole.com/', 'http://www.clevelandviolins.com', None, None, '1592327752', None, None, 'https://locations.nekterjuicebar.com/ll/US/AZ/Chandler/7131-W_-Ray-Rd_*-Ste_-8?utm_source=yelp&utm_medium=link&utm_campaign=Casa-Paloma&utm_content=URL', 'https://www.capriottis.com', 'https://www.myeyedr.com/locations/randolph?utm_source=Yelp&utm_medium=Referral&utm_campaign=Randolph', None, 'http://www.an-immaculate-touch.com', None, 'http://www.artformsalon.com', 'http://alphaaudreyfit.com', '1592327788', 'https://www.bellford.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://parents.berkeley.edu/', 'http://www.7160optima-kierland.com', 'http://www.wholesaleclub.ca/LCLOnline/', 'http://vistadelvalleliving.com', None, 'https://www.coloresdelsolapts.com', None, 'http://www.audreyshopaz.com', 'http://www.goodtimesvip.com/', None, 'http://www.hungryhowies.com/store/hungry-howies-01825', 'https://brooklynmikessubs.business.site/?m=true', None, 'http://www.tidedrycleaners.com', 'http://www.saguarofamilypractice.com', 'http://www.haciendasmexicangrill.com', None, 'http://www.lasvegasbikefest.com/', None, 'http://www.osteria.ca/', 'http://www.hanayagarden.com', 'http://dnacycles.com', None, 'http://www.theroofmedics.com', None, 'http://www.zumiez.com', 'http://www.syntheticgrassstore.com', 'http://www.thebarlv.com', None, 'http://www.equityapartments.com/Arizona/Phoenix-apartments/North-Central/Promontory-Pointe-apartments.aspx', None, '1592327874', 'http://calgaryshawarma.com/', 'https://www.avis.com/en/locations/us/az/goodyear/g5y', 'http://www.carolinashealthcare.org/locations/cabarrus-family-medicine', 'http://www.blazeshops.com', None, 'http://caribbeanpalmtempe.com', 'http://www.SelmanCo.com', None, 'http://www.dunkindonuts.com', 'https://www.haircutmennorthlakecharlottenc.com', 'http://starchemdry.com/', None, 'http://www.folgerkiasouth.com', None, 'http://que-huong-restaurant.business.site', None, 'http://mypolarair.com', None, None, 'http://www.valleygolfcenteraz.com', None, 'https://www.moes.com/find-a-moes/ohio/avon/272?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'https://puresushicolony.com', 'http://roostrealestate.com', 'http://www.maccosmetics.com/stores', 'http://happypawsvets.com', 'https://www.performancebike.com/bike-shop/store/pittsburgh?utm_source=local&utm_medium=organic%20&utm_campaign=yelp', 'https://locations.visionworks.com/ll/US/AZ/Scottsdale/9055-E-Talking-Stick-Way', None, 'http://www.banfield.com/veterinarians/pa/pleasant-hills/phs?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.pasqualespizzeria.com', 'https://chop.ca/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', 'http://www.starbucks.com', 'https://www.johnnyspizzaandgrill.com', None, None, '1592327958', None, 'http://oliverpeoples.com', None, 'http://www.longos.com/store/storedetails.aspx?store_no=34', None, 'http://www.arizonaworkforceconnection.com', 'http://www.bathtubrefinishingphoenix.com/', 'http://ad.doubleclick.net/ddm/clk/283420830;110240480;l', 'http://www.wellroundedmomma.com', 'http://www.hydeparkhomehealthcare.com', 'http://www.ephotoshack.com', 'https://www.applebees.com/en/restaurants-matthews-nc/9616-east-independence-blvd-86050', 'http://www.kiaofstreetsboro.com', 'https://www.themresort.com/dining/studio-b-buffet?utm_source=google&utm_medium=organic&utm_campaign=googlemybusiness', 'http://www.noliarestaurant.com', 'http://altaz933.com', 'http://www.littlecaesars.com/', 'https://www.walmart.com/store/1746/tempe-az/details', 'http://www.deltaco.com', 'http://modoyogaetobicoke.com', 'http://www.quiktrip.com', 'http://www.FirstClassReflexology.com', 'https://www.popeyes.com', '1592328010', 'https://www.rudsak.com', 'http://kimburpetwash.com', None, 'http://www.arvindas.com', None, None, 'https://www.embroidery2.com', 'http://myfavoritesweetshoppe.com/index.php', 'http://www.phoenixfamilymedical.com/', None, 'http://www.pasteleriaelizabeth.com', 'https://www.newyorknewyork.com/en/amenities/pool.html', 'http://www.dollartree.com/custserv/save_user_store.cmd?storeId=5722&inStorePickupZipCode=28227&preferredState=NC&alternateStore=true', 'http://www.ageyecenter.com', '1592328044', 'http://www.americanfreight.com/?utm_source=yelp&utm_medium=social&utm_campaign=profile', None, 'http://www.mendotalakehouse.com/', 'http://www.opportunityvillage.org', None, 'http://www.tacobell.com', 'http://ad.doubleclick.net/ddm/clk/284948209;111995275;v?http://www.delanolasvegas.com/dining/3940-coffee-and-tea.aspx', 'https://www.edojapan.com', None, None, None, None, 'http://www.squeekykleenwindows.com/', 'http://www.speroristorante.com/', 'http://kingpaan.ca', None, 'https://www.circauptown.com', None, 'http://www.nielsenjewelers.com', 'http://www.majorbarbershopcharlotte.com', 'http://www.furryfriendsexpress.com', 'http://www.50caliberracing.com', 'http://www.thevegascafe.com', None, None, None, 'https://www.kindercare.com/our-centers/las-vegas/nv/300791?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=300791', '1592328105', 'http://serenelivingaz.com', None, 'https://www.ediblearrangements.ca/stores/250-7th-Ave-SW-Calgary-AB-T2P-0W6', 'http://greasepaint.org/', 'https://www.pteglv.com/locations/pts-ranch/durango-sunset/', 'http://www.bdiylv.com', None, 'http://cafeteriaandcompany.com', 'https://www.wholefoodsmarket.com/stores/tempenew', 'http://www.appledumplingcafe.com', None, '1592328135', None, '1592328139', 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://www.girlfridayclothing.com/', 'http://www.alliedprintdesign.com', 'https://biz.dominos.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://montereybayfishgrotto.com', None, 'http://trinitycommon.com/', None, 'https://www.interstatebatteries.com/locations/all-battery-center-mesa-az', 'http://www.happybaos.com', 'http://www.backhealthaz.com', 'http://www.brakemasters.com', 'http://www.umamisushi.ca', 'http://www.forever21.com', 'https://www.mandalaybay.com/en/nightlife/lounges-and-bars.html', None, 'http://johnnyfontanes.net', None, 'http://www.crunch50.com', None, 'http://www.accentricktint.net', 'http://www.hainesandkrieger.com', 'http://miniso.ca', 'http://www.coffeetime.ca', '1592328198', 'http://elliescleveland.com', 'http://rauchfamilydentistry.com/', None, 'http://barcento.com', 'http://jaautorepair.business.site', 'http://abraauto.com/abra-auto-location/auto-body-and-glass-repair-shop-peoria-az/', None, 'http://www.greenhousejuice.com', None, None, 'http://ocdandanxietycenterofcleveland.com', 'http://sushiyasu.ca', None, None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', 'https://www.mavistire.com/locations/charlotte-independence-nc.asp', 'http://www.oishimaki.ca/menu_select.asp', 'https://www.wyndhamhotels.com/hotel/14201?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:14201', None, 'http://southpointcasino.com/dining/quick-bites.php', None, 'http://mmgyn.com', None, 'http://www.phxveganfest.com', 'http://porchettaco.com/exchange-tower-location/', 'https://local.albertsons.com/az/mesa/2727-n-power-rd.html', 'https://www.torrid.com/store-details?StoreID=5109', 'http://www.firstnailsandspa.com', None, '1592328264', 'http://www.wrhs.org/research/', 'https://www.AZRekey.com', 'http://insightpestcharlotte.com', 'http://salsarestaurant.ca', None, 'http://www.starbucks.com/store/14175/', 'http://www.aecchampaign.com', None, 'http://www.blissflowyoga.com', 'http://www.cashorpayments.com/home.html', None, 'https://solidmotorcars.com', None, 'http://candinailsalon-com.webs.com/', 'http://www.rocketfireworks.ca', None, 'http://www.arizonalasik.com/', None, None, 'https://dancewithmeusa.com/studio/las-vegas-nv/', 'https://www.sleepcountry.ca', 'http://www.usedcaroutletlv.com', None, 'https://johnsonsunrooms.com', 'http://www.mollymaid.ca/locations/on/toronto-central/toronto-central/', 'http://www.massimosfinemeats.ca/', 'http://www.adatshalompreschool.org', 'https://www.suncoastcasino.com/dine/casual-dining/peng-zu', 'http://www.huronsquaredeli.com', None, 'http://luckyspizza67.com', 'http://foxyhoundpetsalon.com', 'http://www.smartshieldprotection.com', None, 'http://www.sleepnumber.com/?utm_source=Yelp&utm_medium=CPC&utm_term=CTA&utm_campaign=Oy_H71G11Tl3fpAbwOnxiA&cm_mmc=Yelp-_-Yelp-_-WebsiteLink-_-Oy_H71G11Tl3fpAbwOnxiA-904825&tag=904825', None, 'http://www.americanpropertieslv.com', 'http://peterpiperpizza.com/', 'http://www.surlatable.com/browse/storeCalendar.jsp?storeId=110', 'http://www.phoenixpropertymgmt.com/', 'http://www.smokebbqchampaign.com/', None, None, 'http://www.ostaraspa.com', None, 'http://www.trojanpest.com', None, None, 'http://www.bestcuts.com/', 'http://www.mccreative.biz', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.bkvegas.com', 'http://www.agenciahispana.com', None, None, 'https://maricopacountybailbonds.com', 'http://www.amishyard.com', 'http://www.americanlaser.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=paid+search&BannerID=4772', None, 'http://www.lcbo.com', None, 'http://www.andersonaudiology.com', '1592328398', 'https://aria.mgmresorts.com/en/restaurants/salt-and-ivy.html', 'http://thewingspot.ca', 'http://www.starbucks.ca', 'http://www.iwanttiabi.com', None, '1592328412', None, None, 'http://kredohardware.com', 'https://scottsdale.bintheredumpthatusa.com', 'https://www.kidzvillepa.com', 'http://www.JimmyJohns.com', None, None, None, 'http://www.beagle14.com', 'http://www.MickyParker.com', None, None, 'http://www.buffalowildwings.com/', 'https://www.thecanyonsoncolter.com', 'http://www.clevelandfoodcoop.org/', None, 'http://customwaterrefininginc.com', 'http://www.getflipnfit.com/', None, '1592328451', 'http://www.stickirice.com', 'http://www.frysfood.com/', 'http://www.plaza-network.com/', None, 'http://www.brownbagdeli.com/', 'http://www.thesummitpgh.com/', None, None, 'http://lifeisbeautifulfestival.com', 'http://www.JimmyJohns.com', 'http://www.protein-house.com/las-vegas-nv/', 'https://www.take5oilchange.com/locations/nc/charlotte-27/', None, 'http://www.costco.com/warehouse-locations/se-gilbert-gilbert-az-644.html', 'http://www.gotwhatitcakes.com', 'http://www.solonorthodontics.com', 'http://applianceservicerepairphoenix.com', None, 'https://www.mimiscafe.com/locations/scottsdale/', 'https://www.obsessionshairstudio.com', 'http://www.annsbistro.com', 'http://www.uueec.org', 'http://pastissima.ca', 'https://www.airparkdodgechryslerjeep.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', None, None, None, None, None, None, 'http://www.sanremoapts.com/', 'https://www.rentawreck.com/cheap-car-rental-phoenix-AZ.htm', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEAS', 'http://www.cabarruscharter.org', None, 'http://www.menchies.com', None, 'https://locations.theupsstore.com/oh/fairview-park/21887-lorain-rd?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', None, 'https://csilawncareservices.com', 'http://www.gorenter.com', None, 'http://www.elginnursery.com', 'http://www.chiro-medcenters.com', None, 'http://www.highlanderwine.com', None, 'http://www.containerstore.com/locations/showStore.htm?store=PHX', None, 'https://www.skywaterapartments.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=yelpCPC', 'http://www.nextcare.com/locations/az/phoenix-thomas/?utm_source=Yelp&utm_medium=Local&utm_campaign=phoenix_thomas', None, 'http://www.girlsnlashes.ca', 'http://www.studiobymichelle.com', 'https://www.walmart.com/store/2768/mesa-az/details', None, 'http://www.competitiondining.com/events/city', 'http://trakathletics.com', 'http://www.apalla.com', None, 'http://www.medevalclinics.com', None, 'http://www.nighttrainlv.com', 'http://www.bagelworld.ca', 'http://www.redeemerchristianschool.org', None, 'http://www.pizzafusion.com', 'http://thealcazar.com/', None, 'http://www.houseoftoli.com', 'http://www.embergrille.com', None, 'http://www.white-horse-inn.com', 'http://www.fourqueens.com/', 'http://www.banfield.com/veterinarians/oh/parma/par?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.rainbymelodi.com', 'https://calstate.aaa.com/membership/offices/phoenix', 'http://www.marriott.com/cakcy', None, 'http://www.planetfitness.com/gyms/rocky-river-oh-560?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.xtremeescapeadventures.com', 'http://www.omarswindowtintingphoenix.com', None, None, 'http://RGXrims.com/charlotte', None, 'http://www.brandedonecrossfit.org', None, 'https://www.pethealthhospital.com', 'https://udsdebtfree.com/home.php', None, 'http://www.lakeside-coffee.com', 'http://www.executivepawn.com/i', 'https://brooklinecollege.edu', None, None, 'http://www.desertsunembroidery.com/', None, None, 'http://www.pods.com/west-charlotte.aspx', 'http://www.moonlightcarwash.com', '1592328680', 'http://www.poetrynightclub.com', 'http://www.bellebarbershop.com', None, 'https://solexotica.com/169-church-st-toronto.php', 'https://www.fastmed.com/urgent-care-centers/tempe-az-walk-in-clinic-asu/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.mercifrenchcafeandpatisserie.com', None, None, 'https://www.caferio.com/locations/eastern', None, None, 'http://www.caromonthealth.org', 'http://lasvegasreleaf.com', 'http://www.badappletattoolv.com', 'http://www.youraffinityplace.com/', None, None, None, None, None, 'http://www.awakeningseedschool.org', 'http://www.pacini.ca/restaurants/saint-hyacinthe/', '1592328733', 'http://www.narainesbakery.com', None, None, None, 'https://www.maaco.com/locations/nv/las-vegas-12597/?utm_medium=bry&utm_source=yellowpages&utm_campaign=m2597', 'http://fast5towing.net', None, 'http://www.ournoblecompanions.ca', None, 'http://www.bellamage.com', None, 'https://arizonaboyacandheating.com', 'http://pathwayangels.ca/', 'http://www.dedinskymedicine.com', None, None, 'http://www.pizzapizza.ca', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'https://www.frysfood.com/stores/details/660/00694', 'https://www.usps.com/', 'http://comalaparestaurant.com', None, 'http://www.capitalesburgers.com', 'https://locations.checkers.com/nv/las-vegas/4175-e-desert-inn-rd/?utm_source=Yelp', 'http://www.3LakesGolf.com', None, 'http://tacostijuanalv.com', 'http://www.izba.ca', 'http://www.fantasticsams.com', None, 'https://www.camdenliving.com/phoenix-az-apartments/camden-copper-square?cm_mmc=Yelp', 'http://oldschoolhousecatering.com/', 'http://www.lovebugdoula.com', 'http://www.charcut.com/', 'http://www.ivyglobal.ca', 'http://www.yoshisonline.com', None, '1592328817', None, None, 'http://www.cityofnorthlasvegas.com/Departments/ParksAndRecreation/PDFs/CityParksBrochure.pdf', 'http://welbrookcentennialhills.com', None, '1592328826', 'http://www.cpcc.edu', 'https://miraculousmassagelv.com', None, 'http://www.oakley.com/en/store-finder', None, None, None, 'http://brydens.ca', 'http://www.westparksmiles.com', 'http://gametrucks.ca', 'https://www.thomasroofingaz.com', 'https://www.circlek.com/store-locator/us/peoria/9476-w-olive-ave/2706468', None, None, None, 'https://www.pizzaville.ca/stores/hours/2889-derry-road', None, 'https://locations.massageenvy.com/ohio/beachwood/27520-chagrin-boulevard.html', 'http://www.brecksvillechiro.com/dr-adam-mack', 'https://phoenicianoasis.com', None, 'https://www.northerngreensapts.com', 'http://www.poundgyms.com', 'https://www.usps.com/', None, 'http://www.hayashihibachi.com', 'http://www.thebestlittlespa.com', 'http://www.newstalk1010.com/', 'https://littlecaesars.ca/en-ca/stores/48600201/3100-winston-churchill-blvd/mississauga/on/contact', 'http://xangotoronto.com', 'http://www.traderjoes.com', 'http://locator.carolinas.aaa.com/locations/matthews/', None, 'http://www.nellis.af.mil/AirShow.aspx', 'http://thecurvemadison.com', 'http://www.ceastudyabroad.com', 'http://www.toscanavillaliving.com', None, 'http://redrockfertility.com', None, 'https://stores.hallmark.com/az/phoenix/karens-hallmark-shop-phoenix-az-17714.html', None, 'http://www.ljsilvers.com', '1592328926', 'http://daddyospasta.com/', None, None, 'http://www.towbindodge.com', None, 'http://www.firestonecompleteautocare.com/store-detail/356288?lw_cmp=YLP_FCAC_89014&utm_source=YLP&utm_medium=FCAC_89014', 'https://www.eden-lv.com/eden-las-vegas-nv/', 'http://saharapinesah.com', 'http://leobarbershoplv.com', None, 'https://www.orangetheory.com/en-us/locations/pennsylvania/bethel-park/301-south-hills-village/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.SmithFamilyDental.org', None, None, 'http://sugarhavencle.com', 'http://fiveguys.com/', 'http://www.bluebirdstudioclt.com', 'http://www.johnqssteakhouse.com', None, 'http://www.lakeviewbakerycalgary.com', 'https://www.anytimefitness.com/gyms/1825/Maple-ON-L6A-1C6/?utm_source=yelp&utm_medium=local', 'http://www.ambridgewholesaletire.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.onceuponachildmacleod.com', None, 'https://www.jacksonhewitt.com/Tax-Preparation-Services-Locations/NV/Las-Vegas/16812/', 'http://www.tanizakaya.com', 'http://www.partyblooms.com', None, 'http://www.oldtownink.com', 'http://www.sidestogobbq.com', 'http://www.excusespghbarandgrill.com', 'http://www.johannagraff.com', None, 'https://www.thepottery.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.kimnaturalfoods.com', 'http://www.neckerman.com/', 'http://www.galswalkingpals.com', 'https://www.mattressfirm.com/stores/oh/rockyriver/mattress-stores-rocky-river-oh-44116-7748.html', None, 'https://www.zippssportsgrills.com', 'http://www.advancedautoglass.com', None, 'http://www.remixlounge.ca', 'http://www.lhshealth.com/facilities/parkside-villa', 'http://www.motusislandgrill.com/', None, None, 'http://burly-dumpsters.myshopify.com', 'https://www.menswearhouse.com/store-locator/4401?utm_source=yelp&utm_medium=listing&utm_content=4401&utm_campaign=OH', 'http://www.scottsdaleaz.gov/', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.vpcservices.com', 'http://www.shoepalace.com?utm_source=yelp&utm_medium=yelp149', None, None, 'http://www.ohiopetvet.com', 'http://grabhamscandies.com/', None, 'https://www.batteriesplus.com/store-locator/wi/madisoneast/batteries-plus-572?utm_source=yelp&utm_medium=local&storecode=572', 'https://www.cvs.com/minuteclinic/clinic-locator/nv/henderson/8795.html', 'http://www.kettlebellsanctuary.com', 'http://www.alleghenymillworklumber.com', 'https://www.wingstop.com/location/wingstop-421-phoenix-az-85015/menu', 'http://www.miumiu.com', None, 'http://www.brickstreetbakery.ca', 'http://www.morebeattyphotography.com', 'https://www.happyvalleyselfstorage.com', 'http://onyxartevents.net', 'http://www.lepetitnavire.ca', None, 'http://www.bagelsforever.com/', None, 'http://www.innatedogtraining.com', 'http://locations.in-n-out.com/80', None, 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', 'https://www.bannerhealth.com/locations/gilbert/banner-health-center', 'https://www1.shoppersdrugmart.ca', None, None, None, 'http://www.HealthExpressUC.com', 'http://www.northlakedentistry.com', 'http://www.breatherefuge.com', 'https://www.millsnv.com', None, 'https://www.usdermatologypartners.com/sun-city-west/', None, 'http://www.myebus.ca', 'http://www.edmarshalljewelers.com', 'https://locations.cariboucoffee.com/us/nc/charlotte/4327-park-road', None, 'http://www.movingincharlottenc.com', 'http://benetflorentine.com', 'https://www.enterprise.com/en/car-rental/locations/us/az/cave-creek-5033.html?mcid=iyp:8368400', 'https://www.cleanjuice.com/locations/rea-farms/', 'http://www.professionaldrivingacademy.com', 'http://www.mywellcarepharmacy.com', 'http://www.fairwaysapts.com/', None, None, None, 'http://www.AgaveChiropractic.com', '1592329172', 'http://www.southernnevadapaincenter.com', 'http://www.armored-gopher.com', None, 'http://www.regencygarden.com/', 'http://www.verizonwireless.com/stores/wisconsin/fitchburg/fitchburg-324512/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'https://local.fedex.com/oh/medina/office-1624/', 'http://www.panchosmexicanbuffetdfw.com', None, None, 'http://www.skyzone.com/LasVegas', 'http://rincondebuenosaires.com', 'http://www.snapfitness.com/thornhillwest', 'http://paramita.ca', None, 'http://www.realfruitbubbletea.com', 'http://www.charlotteendodontics.com', 'http://healthyhomemkt.com', 'http://www.sescolite.com', None, None, None, 'https://sixmaids.ca', 'http://www.psychicextraordinaire.com', 'http://www.ilovemariospizza.com', 'http://www.rhinoscleaningservices.com', None, 'http://www.usps.com', 'http://www.myoreckstore.com/?utm_campaign=yelp&utm_source=yelp&utm_medium=yelp', 'https://scottsdaledentalexcellence.com', 'http://www.clockdr.com', 'http://www.focusonwhymedia.com', None, 'https://orendaforce.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', '1592329257', 'http://hairnmotionlv.com', 'http://www.littleeinsteinpreschool.com/', 'http://www.sevenjars.com', '1592329266', 'https://www.druryhotels.com/locations/cleveland-oh/drury-plaza-hotel-cleveland-downtown', 'http://www.parnian.com', 'http://www.foodlion.com', None, 'https://www.superiorvanline.com', None, None, None, None, 'http://pu-lv.com', 'http://dollartree.com', 'https://www.shulas.com/shulas-2/cleveland/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCUL', None, None, 'https://www.urbanoutfitters.com/stores/southpark-mall-charlotte', 'http://www.starbucks.com/store/10311/', 'http://www.sallybeauty.com', 'http://crossroadfurniture.ca/', None, 'http://kpopusaonline.com', None, 'https://www.peterpiperpizza.com/locations/gilbert-az/gilbert-williams-field', 'http://www.shermancpas.com', None, 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', 'https://www.dufflet.com', None, 'http://www.specialtouchcleaners.com', 'https://locations.wendys.com/united-states/pa/penn-hills/208-rodi-road', 'https://www.themresort.com/dining/bars-and-lounges/32-degrees-draft-bar', 'http://www.rocksolidautocenter.com', 'http://www.gap.com?tid=gpme000290', None, None, None, 'http://www.sobeys.com/en/stores/sobeys-ajax/', 'http://www.lookstylesociety.com/TownSquare/', None, 'https://premiertanningchampaign.com', 'http://www.fattommyspizzeria.com', 'http://nathanburton.com', 'https://primpandblow.com/locations/phoenix-location/?UTM=yelp', None, 'https://find.shell.com/us/fuel/10005883-1380-north-scottsdale-road', 'http://www.andrewsbbq.com', None, 'http://elmcroft.com/community/elmcroft-of-state-college-pennsylvania/', None, 'http://rodeobraziliansteakhouse.com/', '1592329387', None, None, None, 'http://www.danatire.net/', 'http://winemandental.com/', 'https://www.marriott.com/hotels/hotel-information/restaurant/details/phxwh-w-scottsdale/6500593', 'http://www.timhortons.com/', 'http://www.hansa.skincaretherapy.net/home', 'https://locator.chase.com/az/gilbert/5238-s-power-rd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.planetautomotivegroup.com', None, 'http://www.oakley.com/en/store-finder', None, 'http://scottsdale.kokofitclub.com', None, None, None, 'http://www.safeway.ca', 'http://www.azdanceproject.com/', None, 'https://www.cantorsdrivingschoolaz.com', 'http://www.clevelandkia.com', None, None, 'https://www.t-mobile.com/store-locator/az/scottsdale/scottsdale-fashion-sq-2?cmpid=WTR_SE_YXT_U98MLWB9027148', 'https://www.steppingstoneslv.com', 'http://www.byopnevada.com', 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=1', 'http://www.coffeebean.com', 'http://allergyasthmaclinic.net/', 'http://moderngrove.com', 'http://www.bankofamerica.com', 'http://wendelclarks.com', 'http://www.cougarrunwinery.com', None, 'http://www.cravingstoronto.ca', 'http://www.fernadair.com', None, None, 'http://storelocator.pepboys.com/pepboys/stores/phoenix/cactus/00747', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://yorktownserviceplaza.com', None, 'https://www.dermatologyforanimals.com', None, 'https://www.eatnpark.com', 'http://www.solarcontroltint.com', None, 'https://www.southernfriedchics.com', 'http://kidtownlv.com', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1565', 'http://www.lettiericafe.com', 'http://caspianrestaurantlv.com', 'http://www.canadacomputers.com/', 'https://www.cvs.com/minuteclinic/clinic-locator/az/glendale/17.html', 'http://www.majerles.com', 'http://www.aboveallplumbingaz.com', 'http://www.armeenscakes.com', None, 'http://www.ontheedgehonda-suzuki.com', 'https://www.kimlayson.com', 'http://www.barblevensondogtraining.com', None, 'http://www.sportscardsetcpgh.com', None, 'http://applewoodgallerync.com', 'https://elementsmassage.com/yelp-herbal-ritual-special?loc=Chandler_West', '1592329539', None, None, 'http://www.burlingtoncoatfactory.com/store-details-Store-191--339-Sixth-Avenue--Pittsburgh--PA--15222-2517.aspx?from=15222&id=f7d22de7-2d8e-4020-9d3b-5c710bb133b1', 'http://www.wefavordomestics.com', 'http://www.green-papaya.ca', None, None, 'http://www.mammaspizza.com/', 'http://www.rocketagogo.com', 'http://www.uniquethriftstore.com', 'http://pvallergy.com/', None, '1592329571', 'http://emidioandsons.com/cuyahoga-falls/', None, 'http://canopy-collective.com', 'http://crossroadsbooksandcoffee.com/', None, '1592329586', None, 'http://www.queencityq.com', None, 'http://www.luxhomesohio.com', None, 'https://mysomersetfamilydental.com', None, 'http://www.somethingyoubeauty.com', None, 'https://www.sephora.com/happening/stores/las-vegas-venetian', 'http://www.mcbridemagic.com', None, 'http://phoenixortho.com', None, 'https://primantibros.com', 'http://www.jacksonswash.com/location-84th-avenue', None, 'http://www.abercrombie.com', 'http://www.coolguyslv.com', 'http://www.severinosrestaurant.com', None, 'http://www.familydollar.com', None, None, 'http://www.thechesterfieldshop.com/', 'http://www.gilbertaz.com', None, 'http://www.jadepalacescottsdale.com', 'http://www.tanglesandtea.com/', 'https://www.clecookiedough.com', None, 'https://www.popeyes.com', 'http://www.stella-blu.com', 'https://www.midas.com/nashville/store.aspx?shopnum=3362&dmanum=608001', 'https://www.npmua.vegas', 'http://www.claimjumper.com', 'https://local.fedex.com/nv/henderson/office-1888/', 'https://www.walgreens.com/locator/walgreens-1159+e+southern+ave-mesa-az-85204/id=3670', None, 'https://local.fedex.com/pa/pittsburgh/office-2064/', 'https://locations.wendys.com/united-states/nc/concord/7720-sossoman-lane-northwest', 'http://www.tov-li.com', None, None, 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', 'https://www.dominos.com', None, 'http://appt.eyecarecenter.com', None, 'http://www.thelegalsmith.com', None, 'http://www.tapurfitness.com', None, 'http://www.401logan.com', 'http://www.luxor.com/restaurants/blizz.aspx', None, '1592329730', '1592329733', None, 'http://www.4leasetoday.com', None, 'http://www.reisspropertymanagement.com', 'http://www.mckinley.com', None, 'https://www.redstarvapor.com/stores/vape-shop-mesa-baseline-rd/', 'https://www.thejoint.com/nevada/las-vegas/eastern-and-richmar-36005', None, 'http://www.crownrecyclingcenter.com', 'http://www.familydollar.com', 'https://www.usps.com', None, 'http://www.PleasantDentalAZ.com', '1592329767', None, None, None, 'http://www.bestbilliardslv.net', 'http://downtowncleveland.com/events/winterfest.aspx', 'http://stanncharlotte.org/', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCCS', '1592329787', 'https://aireone.com/locations/mississauga', 'http://www.unisonpropertymanagement.ca', 'https://www.papajohns.com', None, 'http://windsorhyperbar.com', 'http://www.wokofasia.com', None, None, None, None, None, 'http://www.juliabakerconfections.com', '1592329816', 'http://www.holisticlifechiro.com', 'http://ahoylashes.com', 'http://www.frankieswok.net/', None, None, 'https://bargainstorage.com/arizona/self-storage-tempe-az/85281-self-storage/601', 'http://www.SandsAutoBody.com', 'http://bellanailandbar.com', None, None, 'http://www.sunshineacres.org/', 'http://midtownsundries.com', None, None, 'http://pawntnt.com', 'https://www.pizzaville.ca', None, None, 'https://arizona.weidner.com/apartments/az/phoenix/the-trend-at-51/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.crazymocha.com', None, None, 'http://trattorialaterrazza.com', 'http://www.sawyeraviation.com', 'http://www.metrokiaofmadison.com', 'http://www.qualityinn.com/hotel-phoenix-arizona-AZ824?source=pmfyelp&pmf=yelp', '1592329877', 'http://www.universalstonenc.com', None, None, 'http://www.coffee-plantation.com', None, 'http://www.gordonweston.net?cmpid=bxw5_blm_0006', 'http://www.willystreet.coop', None, None, '1592329899', 'https://stores.bestbuy.com/az/phoenix/12645-n-48th-st-250.html/?loc=ns100&ref=NS', 'http://www.johncoatsmortgage.com', 'http://www.simplyvegasrealestate.com', 'http://www.yummeeyogurtaz.com', 'https://www.225streetfood.com', None, 'http://www.hopeactualized.com', 'http://www.kimberlysfacialboutique.com/', None, 'http://www.viaggio.net/downstairbar.html', 'http://www.wildlifelanes.com/', None, '1592329930', 'https://store.vioc.com/oh/south-euclid/1856-warrensville-center-road-44121-060096', 'http://www.absolutefootcarelv.com', '1592329938', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.centerrascottsdale.com', 'http://www.subway.com', 'https://www.mainevent.com/location/arizona/gilbert/85295?utm_campaign=localmaps&utm_medium=organic&utm_source=yelp', 'http://www.SheaBrie.com', 'http://www.corporatejobbank.com', None, 'https://lhlservice.com', 'http://www.ultrasmoothskin.com/', 'http://www.themetapartmenthomes.com?campaign_code=yelp_The_Met_at_3rd_and_Fillmore_AZ_85004', 'http://www.congeestar.com/', None, None, 'http://www.rossocoffeeroasters.com', None, None, 'http://helmshomeinspections.com', 'http://www.vanquishcarcare.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://voguenailspacharlotte.com/', 'http://www.infinityfloraldesigns.com', 'http://thesaloonsalon.com/', 'http://urban-planet.com', 'https://www.reddevelopment.com/camelback-colonnade/', None, 'http://www.aftontavern.com/home.aspx', 'https://bmcmattress.com?utm_source=Yelp&utm_medium=organic&utm_campaign=PhoenixJanMar2018&utm_content=website-organic', 'http://www.centralazsupply.com', 'http://www.pods.com/pittsburgh.aspx', '1592330010', 'http://www.lowes.com', 'http://www.itechautocenter.com/', 'https://www.chapters.indigo.ca/en-ca/home/storelocator/storedetails/965', None, None, 'https://www.caferio.com/locations/gilbert', 'http://www.e11even.ca', 'https://www.dnatactical.com', 'https://locations.wendys.com/united-states/oh/westlake/29778-detroit-road', 'http://www.suntimeluxury.com/', 'https://locations.theupsstore.com/az/glendale/7942-w-bell-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://chatterboxsalon.co', None, 'http://www.mcgugans.com', 'http://ragstock.com/stores/madison', 'http://www.frontlinehome.com', None, 'http://www.chevron.com', 'https://wisgaragedoors.com/madison', 'http://www.lovelandgroup.com', 'http://www.aliveandfreehypnosis.com', 'http://www.wirigortho.com', 'http://www.discoverlennyboy.com', 'http://www.paradisecantinalv.com', None, None, 'http://knar.com/toronto/', 'http://www.spynga.com/locations-chagrin-falls/home', '1592330080', None, None, 'https://www.calgarylimousine.com', 'https://locations.wendys.com/united-states/oh/independence/6899-rockside-road', 'http://grandslamcustard.com', 'http://www.bluewaterpoolsaz.com', 'http://mastros3spot.com', '1592330099', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'https://tpltauto.com', 'http://www.mississaugaautocentre.ca', None, 'http://www.fringeinc.ca/', 'https://locations.wendys.com/united-states/oh/parma-heights/6530-pearl-road', 'http://www.theclevelandhostel.com', 'http://thehophouse.com/index.html', 'http://www.sleepnumber.com', 'http://www.mississaugagrand.com', None, None, 'http://nveyesurgery.com', 'http://www.dunkindonuts.com', 'http://www.starbucks.com', 'http://cenatabella.ca', None, None, 'http://www.beautynailsandspascottsdale.com', 'http://www.katzdogswellness.com', None, 'http://www.findlaynorthvw.com', 'http://www.marriott.com/hotels/hotel-information/restaurant/clesc-cleveland-marriott-downtown-at-key-center/', 'http://www.royalcoffeebar.com', 'https://www.greatclips.com/salons/1594', None, 'http://www.TheCharlotteFair.com', 'http://www.landerolearningcenter.com', None, '1592330163', None, 'http://www.ajspestcontrol.com', 'http://planetnails.ca/index.html', 'http://www.kitchencollection.com', None, None, None, 'http://www.chevron.com', 'http://www.regus.com', None, 'https://1800theeagle.com/phoenix-camelback', 'http://www.scottsdaleluxuryvillas.com', None, 'http://www.azstorage.com/self-storage-locations/chandler/west-chandler-self-storage-85224', None, 'https://www.charlotte.inkanivy.com', 'http://thescorpio.com/', 'http://superaquaclub.com', None, None, 'https://www.yogurt-land.com/locations/view/1174/avondale?distance=1.3', 'http://www.foxvalleyelec.com', None, 'http://dierkswhiskeyrow.com/tempe', 'https://www.westlakelibrary.org', 'https://www.outsourcedatarecovery.com', 'http://www.pro-am.ca/', 'https://www.medexpress.com/location/pa/allison-park/app/', 'http://www.anjubarandeatery.ca', 'http://www.starbucks.com', 'http://www.livetalentnow.com', 'http://www.lasvegasnational.com', None, 'http://www.tgifridays.com/index.htm', 'http://baxterscigars.com', '1592330246', 'http://www.nipperspgh.com', 'http://www.nextcare.com/locations/az/avondale/?utm_source=Yelp&utm_medium=Local&utm_campaign=avondale', 'http://www.azcountryclub.com', None, 'http://www.bluespooncafe.com', None, 'https://stores.dickssportinggoods.com/pa/mccandless/1142/', None, None, None, 'https://www.keywestautosales.com', 'http://www.lvtreeservice.com', None, 'http://megmeyerphotos.com/', '1592330279', None, 'http://www.celebritypizzas.com', None, 'http://www.quiktrip.com', 'https://ad.doubleclick.net/ddm/clk/401355505;201491930;s', 'http://www.phoenixdiscountsilkflower.com', None, 'http://www.buyinlasvegas.com', 'https://paintersofthevalley.wordpress.com', None, None, 'http://www.downtowncamera.com/', 'http://chermacbuilders.com/', 'http://www.skinandcancercenterofarizona.com', 'https://www.morgancommunities.com/apartments/nc/charlotte/atkins-circle-apartments/', 'http://www.bankofamerica.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, 'http://www.sidecarrestaurant.ca', None, 'http://thebrilliantbagel.com', 'http://houseofvr.com', 'http://jaysshop.ca', None, 'https://www.bathandbodyworks.com', None, None, 'http://www.playitagainsportsscarborough.com', 'http://www.scottsdalemusiccompany.com', 'http://mesadrummer.com', None, 'http://frankandbeancoffee.com', 'http://www.fuzziwigscandyfactory.com', 'https://www.locopatron.com', 'https://hihidonuts.business.site', 'http://store.sony.com', 'http://mjafari2.tripod.com', None, 'http://www.colonspas.com', 'https://www.ikea.com/us/en/stores/pittsburgh/', 'http://www.gtaworkingdogsinc.ca', '1592330379', 'http://www.toyotaonthepark.ca', 'https://www.goldfishswimschool.com/hudson/', 'http://Grandmamato.com', 'http://www.brazilianbbq.ca', '1592330391', None, None, 'http://www.downtowncleveland.com/living/amenities/downtown-dog-park.aspx', 'https://www.walmart.com/store/1598/phoenix-az/whats-new', None, 'http://www.summerlabelle.com', 'http://www.marcheleos.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://allinhomerepair.com', 'http://www.kyrenefamilydentistry.com', None, 'http://www.copart.com/us/Locations/57', 'http://www.apple.com/fashionshow', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.blisscupcakes.com/', 'http://www.elpatronwisconsin.com/home.html', 'https://www.dufflet.com', 'http://www.chopwoktalk.com', 'https://www.brighton.com', 'http://www.rightimehomeservices.com/', 'http://www.ecacademy.com', None, None, 'http://BluBurger.com', 'http://www.bestfriendspreschool.com', None, 'http://www.ndandacuisine.com', 'http://comeshootwithme.com', None, None, 'http://bibersgarage.com/', None, 'http://www.diamondbeachsports.ca', None, 'http://www.yangschicken.ca', None, 'http://www.azpain.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/127+South+Main+Street-Davidson-NC-28036/storeid=6402?cid=ps_ylp_2020', 'http://www.willsplumbingllc.com', 'https://www.publicstorage.com/arizona/self-storage-phoenix-az/85027-self-storage/1113?pid=wyelp&CID=1245&CHID=AFL', 'http://www.gwendolynehats.com', 'http://www.pilatessol.com', 'http://www.bestvetcharlotte.com/', 'http://www.KitchenCabinetsLV.com', 'http://potatopia.com', None, 'http://canyonfalls.com', '1592330515', 'http://www.hohocherryhousenc.com', 'http://silverleafdayspa.ca/', 'http://idleonbloor.com', 'http://www.greengrotto.ca', None, 'http://LuckysLiquor.com', '1592330533', None, 'http://modish-studios.com/', None, 'http://freshandeasy.com', 'https://www.schueys.ca', 'https://delitavern.com', 'http://coolrenewalspa.com/', 'http://camprhino.com', None, 'https://locations.schnucks.com/il-urbana-720', 'http://blossomgarden.ca', 'http://www.rockerworldofaz.com', 'http://www.sunsetshutters.net', 'https://www.aria.com/en/casino/poker.html', None, None, 'http://www.blinemovers.com', None, None, 'http://www.theparkmeadowapartments.com', None, None, 'http://www.zoup.com/menu.html?location=ZOU00173', 'http://www.barkavepet.com', 'https://www.pizzahut.ca/store-details/store-R32814/pizza-hut-Mississauga', None, 'https://alldermatology.com', None, 'https://www.tuscanylv.com/restaurant/tuscany-gardens/', 'http://www.jpco.ca/', 'http://www.realfruitbubbletea.com', None, 'http://www.toronto.ca/parks/parks_gardens/eglinton.htm', 'http://www.tandooripalacelaval.com', 'https://www.hellotech.com/us/nv/clark/las-vegas', 'http://www.RenewedBodyMassageAZ.com', '1592330622', '1592330625', 'http://www.clevelandymca.org', 'https://www.appleone.com/?yelp_track', 'https://www.hardees.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, None, 'http://www.blueowlcatering.com', 'https://scottsdalebodyandsoulspa.com', None, 'http://www.lasvegasurgentcare.com', 'http://www.ragecycles.com', 'http://www.thefreshmarket.com/', 'http://www.aronanailspa.com/index1.html', 'http://pavelsjewelry.com/', None, 'http://www.stillsconstructionllc.com', None, 'http://www.sdmi-lv.com', None, 'http://www.celebritytanning.com', 'http://yackconstruction.net', 'https://www.epiphanydermatology.com', 'http://www.toysrus.com/family/index.jsp?categoryId=2255956&camp=MISC:yelp:store:page:tru:111910', 'https://www.thevillageatwestpoint.com', None, 'http://www.leisuretimewarehouse.com', 'http://www.lecreuset.com/stores/scottsdale-quarter-scottsdale-az', 'http://www.yanvechiarellichiropractic.com', None, 'https://www.aviatordanforth.com', 'http://raspadossolaris.com', None, 'http://wowwash.com', 'http://www.maviswinkles.com', None, None, 'http://retablo.com', '1592330708', 'http://www.strivedreams.com', '1592330713', '1592330716', 'http://www.carolinasdentalcentermatthews.com', 'http://www.pizzanova.com', 'https://www.rallyhouse.com/rally-house-fairview-park', 'https://www.bankofamerica.com', 'http://yourspacesalons.ca/volum', 'http://www.gotrootshairsalon.com', None, None, 'http://www.monsterplow.ca', 'http://www.hobbylobby.com/store/HOB-LOB+%23380?lat=33.4763518&long=-112.2980119', 'https://www.smartstyle.com/en-us/locations/nv/las-vegas/located-inside-walmart-3473-haircuts-3334.html', 'https://www.choicehotels.com/CN291?mc=blypypaf', 'http://providencevets.com', 'http://whasn.com/main/doctors/15/16', 'http://www.campbellmechanicallv.com', 'http://www.hrrocksinonorthfieldpark.com', 'http://www.bombay.ca', None, None, None, 'http://www.fyeo.net', 'https://www.horizondentalclt.com', 'http://gyubeejapanesegrill.com', 'http://www.healinghouseinstitute.com', None, None, 'http://www.meckabc.com', 'http://www.dogguru.com', 'https://www.sourceforsports.ca/fr-CA/Stores/129-Sport-Campus-Verdun-La-Source-du-Sport.aspx', None, 'https://www.floydsbarbershop.com/scottsdale/', 'http://www.lululemon.com/newmarket/uppercanadamall?cid=yelp', 'http://www.laxerlongandsavage.com', '1592330790', 'http://www.arizonawoodwork.com', None, 'https://www.sprint.com/storefronts/bd/sprint-homestead-pa-15120-fcs-686/?ecid=SEO:Yelp:2020_Q1:LastMile', None, 'http://www.salongrizza.com', 'http://www.clevelandsegwaytours.com/', 'http://www.bestcofoodmart.com', 'http://www.mcnultyroofing.com', None, None, 'http://www.charlotteaquatics.com', 'http://www.top-honors.com', 'http://www.tntcarwash.biz', None, 'http://www.eyebrowsrus.com', 'http://www.crismonsbaby.com/', None, 'http://www.mesamotors.net', 'https://erusenergyarizona.com', 'http://www.fishtalesflyshop.com/', 'http://www.topnotchbarbeque.com/', 'http://www.maxsally.com', 'https://www.discoverpinecrest.com/tenants/sweeties-big-fun/', 'https://www.wyndhamhotels.com/hotel/52784?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52784', None, 'http://www.forestridgeapts.net', 'http://bridgetscreativehairstyles.com', 'http://www.5starconcord.com', 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://subway.com/', None, None, 'http://www.wildwestdoor.com', 'http://www.jlcolesalon.com/', 'http://www.gotronics.com', None, '1592330870', 'http://www.absolute-glass.com', 'http://whcdaycare.ca', '1592330876', None, 'http://www.francishandymanrepairs.com', 'http://hyreconstruction.com', 'http://www.linlawgroup.com', None, 'http://my.chiromatrixbase.com/drormand.com', 'http://savondrugs.com/', 'http://www.metropizza.com', None, 'http://www.shearorganichair.com', 'http://www.jadethreadandwax.com', 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=357', 'http://waternicetempe.com', 'http://www.silkroom.ca', 'http://www.davidsonbeverage.com', 'http://www.vietfooddelivery.com/', 'http://www.sleepnumber.com', None, None, 'http://Blindsprolv.com', None, None, None, 'http://renegadescottsdale.com', None, 'http://www.mudan.ca', 'http://www.cashamerica.com/SUPERPAWN-stores/NV/LASVEGAS/LV12', 'https://www.ecftrainingpittsburgh.com', 'https://www.abcnissan.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', None, None, None, 'http://www.crepedelicious.com', 'http://assuredautobody.com/', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', 'http://www.madeinargentinalv.com', None, 'http://www.fireflysminigolf.com', 'http://www.einsteinbros.com', 'https://artofmusiclv.com', 'http://www.epicroofing.ca', 'http://www.evpcoffee.com/default.htm', '1592330973', None, 'https://www.chick-fil-a.com/arboretum', 'http://www.gianteagle.com', None, 'http://1stoptitleloans.com/', 'http://www.grandliving.care', 'http://hibsyoga.zenplanner.com', 'http://www.stevemadden.com/custserv/store_details.jsp?storeId=1005', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, 'http://www.baskinrobbins.ca', 'http://happyfootspa.ca', 'http://www.bexleyspringsfarm.com', None, None, None, 'http://www.wfsandwiches.com', 'https://www.northstarhome.com', 'https://www.risqueclothing.ca', 'http://grayhawkdentalassociates.com', None, None, 'http://www.yankeelady.ca', 'http://www.shopthegreatescape.com', None, 'http://cityoven.com/', 'http://gabbys.ca', None, None, 'http://www.yalaspizza.com', 'http://www.audiroyaloak.com', 'http://charlotteairport.house.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_cltxc_en_homepage_desktop&code=YB', 'http://perfecteviction.com', None, None, 'http://lakewylieeuro.com', 'https://www.l7-marketing.com', 'https://www.wyndhamhotels.com/hotel/01789?tel=18003291073&iata=00093785&cid=fe:di:20161220:yl:pp:dius:01789', 'http://www.goldenspoon.com', None, '1592331076', None, 'http://curlyhairinstitute.com', 'http://www.accreditedpool.com', '1592331086', 'http://www.scottsdaleaz.gov/', None, 'https://www.foodlion.com/stores/sc/fort_mill/2204/', None, None, 'http://www.lifecarechiropractic.com', None, 'http://www.broadwaylashvegas.com', 'http://www.sewprettyhair.com', None, None, 'http://www.classicimagedance.com', None, None, 'http://www.serklandpools.com/', None, 'http://www.catcareclinic.net', 'https://www.uptownbrie.com', None, 'http://www.matinasbridal.com', 'http://www.poolsteward.com', 'https://www.fallsmotorcity.com', None, 'https://larderdb.com', 'http://lesmoulinslafayette.com', 'http://www.pizzahut.com/', 'http://mvsc-gilbert.com', None, 'http://www.haireffectssalon.com', 'http://www.salonnarichunites.com', 'http://www.gamestop.com', 'https://sunsetmoving.com/international-las-vegas-y/', 'http://www.fifty101apts.com', 'http://leesliquorlv.com/locations/lake-mead-tenaya-2/', None, None, 'http://www.ae.com', None, 'http://www.mallingereyecare.com', 'http://www.totsunlimited.net', None, 'http://christensenfamilydentistry.com/', 'http://www.energreencarpetcleaning.com/', None, 'http://www.junkdrs.com', None, 'http://www.maestrosbistro.com/', None, 'http://a-1coins.com/', 'http://www.european.ca', None, 'https://www.hilton.com/en/hotels/yuldnes-embassy-suites-montreal/?SEO_id=YELP-ES-YULDNES', 'http://www.amugyoucantrust.com', '1592331206', 'https://www.torgensonlaw.com', 'http://monroysautoglassllc.com', 'http://www.barringtonregentapts.com/', 'http://www.culinaryproslv.com/', 'http://www.fiddlerscourtyard.com', 'http://www.techrepairgeek.com', 'http://www.mulinopastry.com', 'http://www.go-bistro.com/', None, 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/lakewood-hospital', 'https://kuhlentertainment.com', 'http://www.asiagostuscanitalian.com/pittsburgh-pa/', 'http://www.theassemblyguys.com', 'http://www.slidingdoorco.com', 'http://www.dreap.net', 'http://www.mybobs.com?utm_medium=local&utm_source=yext&utm_campaign=yextlistings&utm_term=wisconsin&utm_content=176%20madison%20wi', 'http://www.greatclips.com', 'http://www.philadelphiasandwichcompany.com', 'http://www.beewisepestcontrol.com/', 'http://www.crossfitforbidden.com', None, None, 'http://hrflvegas.com', None, 'https://doubletree3.hilton.com/en/hotels/arizona/doubletree-by-hilton-phoenix-north-PHXNTDT/index.html?SEO_id=YELP-DT-PHXNTDT', 'http://www.firstfoodbank.org', '1592331267', None, 'http://www.harrisburgnc.org', None, 'http://macslashandskinstudio.com', 'https://locations.theupsstore.com/nc/weddington/13663-providence-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.metheartist.com', None, 'http://www.badospizzagrill.com/', 'http://www.theshadetree.org', 'https://rainforestplumbingandair.com', None, None, 'http://www.eyelike-saigonoptical.com', None, None, 'https://twomenandatruck.com/movers/az/phoenix/scottsdale-south', None, None, 'http://www.gilesplumbing.com', 'http://www.mebapts.com/', 'http://www.longospizza.com', '1592331317', 'http://www.yogamandala.ca', 'http://joestireshopaz.com', 'http://www.bjslasvegas.com/locations/bjs-south', 'https://suncitymechanical.com', 'http://thewindowdepot.com', 'http://www.azhandman.com', None, None, 'http://www.trustworthylv.com', 'http://www.innonthemexicanwarstreets.com', 'http://www.concentra.com', None, 'http://celenasbakery.com', None, None, 'https://barrospizza.com', '1592331358', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Cleveland-Heights-OH-44118/766054/', 'http://www.cirinophoto.com/mp_client/gallery.asp', 'http://www.lovepoolcare.com', 'http://www.justdoorslasvegas.com', 'https://www.troplv.com/dining/trago-lounge', 'http://danielscoffeeandmore.com', 'https://www.papamurphys.com/store-finder/nc/matthews/NC051/?dist=2.4+Miles', 'https://www.mcalistersdeli.com/locations/nc/charlotte/9864-rea-road-suite-a-1237', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://jacarcolorlounge.com/contact.html', None, 'http://www.culinaryoccasions.com/', 'http://www.portofsubs.com', 'https://www.carstar.ca/en/locations/on/richmond-hill/carstar-wilson-niblett-richmond-hill-16037/', 'http://leesliquorlv.com/locations/sunset-office/', 'http://www.fixintoeat.com', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/deforest/defwi/hoteldetail', None, 'https://www.ulta.com/stores/goodyear-az-157', None, 'http://www.eddo.biz/', 'http://duffysmtl.com/', None, 'http://www.gobellissimos.com', 'https://phoenixazmidwife.com', None, 'http://www.zpizza.com', 'http://www.greatclips.com', 'http://balunsd.com', 'http://seattlegoodwill.org/shop/locations/monroe?utm_content=Monroe&utm_medium=Yelp+Page&utm_source=Referral&utm_campaign=Yelp+Branded+Pages', 'http://www.homesteadanimalclinic.com', 'http://mickeyandmooch.com/locations/lake-norman', 'https://lavishbeautysalonaz.com', 'http://huntersvilledentist4u.com/', 'http://flowersbeer.com/', 'https://www.pteglv.com/locations/pts-pub/stewart-nellis/', None, 'http://www.launiquelasercentre.com/contact.html', 'http://www.doubledouble.ca', 'https://www.aurorawinterfestival.com/toronto/', None, None, None, None, 'http://www.lemonhousecleaning.com', 'https://keithclinic.com/locations/north-charlotte/', 'http://autovillerepair.com/', None, 'http://www.frontierlandscapinglv.com', 'https://www.nike.com/us/en_us/retail/en/converse-factory-store-phoenix-premium-outlets', 'http://www.lina-furnishings.com/', 'http://www.extramileautospa.com', 'http://www.NevadaConstructionLV.com', 'http://garageoneenterprisesinc.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3870+Washington+Road-Mcmurray-PA-15317/storeid=5101?cid=ps_ylp_2020', 'https://royaltintlv.business.site', None, 'https://www.thebarkleypethotel.com', 'https://www.dsw.ca/en/ca/', None, 'http://ad.doubleclick.net/ddm/clk/283420830;110240480;l', 'http://www.birdhouseonthegreenway.com/', 'https://www.naturalgrocers.com/store/chandler', 'http://www.oldtowntavernaz.com', 'http://gogreenvalet.com/', 'http://manchuwok.com', 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', 'http://www.eliteshuttersandblinds.com/contact-us/north-phoenix', 'http://anestateintime.com', '1592331529', 'http://fivepointshotchicken.com', 'http://www.samuraisams.net/stores/5001', None, None, 'http://www.cutiebabyboutique.com', 'http://www.rochsplace.com', 'http://www.marshallsautorepair.com', None, 'http://www.radiusrestaurant.org', 'https://themedicarestore.com', None, None, 'http://vistalandscape.com/', 'http://www.rusticdecorstore.com', 'http://www.leightonmd.com/', None, 'http://www.jacktownrideandhunt.com', 'https://aztrailriding.com', 'http://www.pizzapizza.ca', 'http://www.nutritionbyjoey.com/', 'http://www.cfwellness.com', 'https://www.repairngo.com', 'http://www.targethealthltd.com/', 'https://www.shatleyblue.com', None, 'http://www.ocotillointernalmedicine.com/', 'https://www.expresspros.com/wlasvegasnv/', 'http://www.regalbathandkitchens.com', 'https://locations.churchs.com/az-phoenix-7235', None, None, None, None, 'http://www.quiznos.com', None, 'http://www.greenvalleyranchresort.com/entertainment/quinns-irish-pub.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=GVR&utm_content=GVR-PROPERTIES&utm_campaign=GVR-YELP', None, 'http://www.rei.com', 'https://www.premiumoutlets.com/outlet/las-vegas-south', None, None, None, '1592331625', None, 'http://www.simonprotection.com', 'http://www.overnightgreetings.com', 'http://www.joyandassociates.com', 'http://www.fullforcelv.com', 'http://www.yogurtology.com', 'http://www.scottsdaleserrentoarizona.com', '1592331643', None, None, 'https://www.ars.com/cleveland', '1592331652', 'http://pixiescandy.com', None, 'http://www.chazen.wisc.edu/', None, 'http://www.tutortime.com/your-local-school/glendale-az-6081/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://www.dasbrezelhaus.com', 'http://www.slugbugpools.com', 'https://pennhillsmaids.blogspot.com', None, 'http://www.eyecandyopticalcenter.com/', 'http://www.scholesperio.com', 'https://www.steinhafels.com', None, None, 'http://www.wahwibolton.com', 'http://southwestgardener.com', 'http://knockout-fitness.com/locations/goodyear', None, 'http://www.ntb.com/store/6154/gastonia-nc-28054-0626?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, 'https://SunPointAppraisals.com', 'http://www.toptailoringmadison.com', 'http://www.kennyslawn.net', 'https://www.californiaclosets.ca/en/how-we-work/showrooms/calgary-showroom/?CC5=32008&CC6=30593&utm_source=directory&utm_medium=local&utm_content=AB176-M2-SR1', None, 'http://www.dunkindonuts.com', 'http://www.doorkinglasvegas.com/', None, 'http://www.viptickets.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'https://www.ashleyfurniturehomestore.com/furniture-stores/united-states/az/phoenix/scottsdale?cmpid=2016YELP', None, None, None, 'http://www.alspizza.com', 'http://www.roostercoffeehouse.com', None, 'http://www.icecreamatsamslv.com/', 'http://nspestcontrol.com/', 'http://stickscigarsaz.com', 'http://www.eandmautocenter.com', 'http://www.fossil.com', 'http://jonriccharlottemedicalspa.com/', '1592331754', None, 'http://glamournailspacalgary.com', 'http://www.fatbastardburrito.ca', None, 'http://www.cfi-nv.com/', None, 'http://fitfactoryfitness.com', None, 'https://locations.mrtire.com/nc/indian-trail/13808-e-independence-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.cuchulainns.ca/', 'https://www.capriottis.com', None, None, None, None, 'http://www.bunkersglass.com', 'http://www.pediatricmedicalassociates.net', 'http://www.GroundControlFlooring.com', 'http://www.grapeexpectationslasvegas.com/', '1592331794', 'https://atirestoration.com/247response?utm_source=yelp&utm_medium=ad&utm_campaign=phoenix', 'http://www.sandsglendale.com', None, 'http://www.angelnailspa3015banksville.com', 'http://www.arizonadigestivehealth.com/providers/michael-r-mills-md/', None, 'http://www.beyondpest.com', 'http://leesliquorlv.com/locations/lake-mead-tenaya-2/', None, 'http://www.butterflybraces.com/', 'http://www.justbecausemassagetherapy.com', 'http://www.talkingstickresort.com/', None, 'http://harmonydentalofaz.com', 'http://www.advancedplumbingservices.com', None, 'http://charlottecentercity.house.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_cltxd_en_homepage_desktop&code=YB', None, None, 'http://pittsburghnorthshore.place.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_pitzn_en_homepage_desktop&code=YB', None, 'http://golden94.webs.com', 'https://www.kohls.com/stores/oh/parma-242.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.cardinalcu.com', 'http://premiumcoachgroup.com', 'http://www.alcomaonthegreen.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/7990+East+Us+Highway+36-Avon-IN-46123/storeid=6559?cid=ps_ylp_2020', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2faz%2fphoenix%2fchandler&sisearchengine=1524&siproduct=2628_Bus', 'http://www.rskane.ca/', 'http://www.kwbiltmore.com', None, 'https://www.cosmopolitanlasvegas.com/pools-cabanas', None, None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.arborsondecatur.com', None, 'http://www.peoriacharter.com', 'http://luckystreakatlaslasvegas.restaurantsworld.online', 'http://pizza.dominos.ca/North-York-Ontario-10286', None, 'http://lgbtcleveland.org/index.html', 'http://www.amppersonalfitness.com', 'https://www.stylelushsalon.com', 'https://ad.doubleclick.net/ddm/clk/434333471;236814625;e', 'http://www.swisschalet.com', None, 'http://www.ubreakifix.com/locations/summerlin', 'https://www.discounttire.com/store/az/peoria/s/1687?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'https://www.solismammo.com/arizona/chandler/', None, 'http://www.ultrasoundtoronto.ca/', None, 'https://www.jerseymikes.com/2025', None, None, '1592331930', None, 'http://vipbarbershopaz.com', 'http://www.osborneplumbingdrain.com', 'http://esmebeautiful.com', 'http://amalficoastrestaurant.ca', None, None, None, 'http://pizzayourway.com', None, None, 'http://jackastors.com/location-map/22/', None, None, 'http://strandshair.ca/', 'http://fiitfactorylv.com', None, 'https://www.smalv.com/OurCenters/SurgeryCenter', '1592331979', 'http://www.motivesalon.com', 'https://embassysuites3.hilton.com/en/hotels/arizona/embassy-suites-by-hilton-scottsdale-resort-SCTESES/dining/index.html', 'http://www.goodwill.org/hours-directions/?id=5280&addr=53719', 'http://www.spartanpharmacy.com', 'https://www.hendersonhospital.com/services/emergency/eratgreenvalleyranch', '1592331992', 'https://colburnlvcom.godaddysites.com', 'http://www.inthebliss.com', 'http://www.tokyotosushi.com', 'http://www.brotherstailorsaz.com', 'http://www.wolfpacktattoo.com', 'https://www.boxerluv.org/info/display?PageID=12320', 'http://www.heritagehillspa.com', 'http://adobeclinic.com/', 'http://lucididistilling.com', 'http://www.secondcity.com/?id=theatres/lasvegas', None, None, 'https://www.louisianaffccharlotte.com', None, 'http://www.carolinaweddingbelle.com/', 'http://www.gamestop.com', 'http://www.inthezonespa.com', 'http://www.bk.com', None, None, 'http://www.fuelforgold.com/', 'http://www.comfortfootspa.com', 'https://www.beautifuladdictions.net', 'http://www.acruzinclip.com', 'http://www.chefguru.ca', 'https://www.usps.com/', None, 'http://leesatamember.com/locations/northscottsdale/', None, None, None, 'http://www.walmart.com/', '1592332070', 'https://www.voluptuousclothing.com', 'http://helpadogsmile.org', None, 'http://www.valuevillage.com', 'http://fyzicalpilates.com', None, '1592332086', 'https://www.dentalchoice.ca/company/locations/university-calgary-dental-choice/', 'http://www.packsanddogs.com', 'http://www.villasalerno.com/', 'http://www.banfield.com?utm_source=yelp&utm_medium=PAID&utm_content=yelp_general&utm_campaign=YelpPaid', 'http://www.cartierclassic.com', 'https://www.rvdealermesa.com', 'http://shawarmaroyale.com', 'http://bellalilybridal.com/', 'http://Www.miraclemethod.com/phoenixwest', None, 'https://www.zippssportsgrills.com', 'http://www.quiktrip.com', 'http://www.georgiosofp.com', 'https://www.target.com/sl/mccandless/1218', 'http://www.tropicalsmoothiecafe.com', None, None, 'https://budgetblinds.com/SouthEastChandler/?utm_source=yelp&utm_medium=naf-listing&utm_campaign=NAF-LOCAL-YELP', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'https://www.nofrills.ca/store-locator/?storeId=3620', None, 'http://www.lawncareklemmers.com', 'http://www.starbucks.com', 'https://hawaiianexperiencespa.com', None, '1592332145', 'http://www.aerotek.com/locations/united-states/arizona/phoenix.aspx', None, None, 'http://www.redrocklasvegas.com/dining/cabo.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=RR&utm_content=RR-PROPERTIES&utm_campaign=RR-YELP', None, 'http://hitechautopittsburgh.com', None, 'http://www.vineyardaz.com', None, 'http://www.ohmonsushi.com', 'http://marina-dosa-tandoori-grill-westwinds-ne.business.site', 'http://www.hotdogonastick.com', None, 'http://www.humanproduction.com', 'http://www.framingfactory.ca', None, 'http://www.clevelandkia.com/service-home.htm', None, 'https://www.calgaryrekeylockworks.com', 'http://www.reasitaliancucina.com', 'http://marlenjewelers.com', 'http://esagehealth.com/', None, None, None, 'http://www.poindextermoving.com', None, None, None, 'http://www.westvalleydentallv.com/', 'http://www.thaiprincess.ca', None, None, 'http://salestalentagency.com/', None, '1592332225', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'http://www.gramarusa.com', 'http://mypilatesphysique.com/', 'http://www.angieilg.com', 'http://www.rebeccarichardsonmortgage.com', 'http://www.nochempool.com/', 'http://opasouvlaki.ca?utm_campaign=enhanced-profiles&utm_medium=website-click&utm_source=yelp', 'http://www.maricopa.gov/publichealth/Programs/Vitals/default.aspx', 'http://tastytourstoronto.com', '1592332248', 'http://www.nynyhotelcasino.com/entertainment/bars/center-bar.aspx', 'http://www.vanillapastry.com', '1592332257', 'https://www.thecoreinstitute.com', None, None, 'http://www.strategicintelligenceservices.com', 'http://pennmacfs.com/', None, None, 'http://topchoices.ca', None, 'https://dublincalling.com/calgary/', None, 'http://www.nbarizona.com', None, 'http://yourreddoorteamaz.com', 'http://www.classicv-dubs.com', 'http://www.saltedroot.com', 'http://www.longjohnsilvers.com/', 'http://www.gotosleepcenter.com', None, None, None, None, 'http://www.azbesttire.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.appetitexpress.com/', 'http://www.drewbrotherscustoms.com', '1592332319', None, 'http://www.crownanddragon.com/', 'http://www.orchidpastry.com', 'https://www.luckyshoes.com/stores/new-balance-cleveland-van-aken-center/', 'http://customcreaturespetshop.com', 'http://www.torontobusco.com', 'http://www.zoespizzeria.com', 'http://salontatiana.com', 'http://www.chandanfashion.ca', 'http://www.starbucks.com/store/9334/', None, 'http://escapechambers.com/contact-madison-2/', 'https://estheticsolutions.com', None, None, 'http://www.clevelandacupuncture.com', None, None, 'http://www.heart2heartwellnesscenter.com', 'http://www.zreteam.com', 'http://onebrilliant.com', None, 'http://www.pizzahut.com/', None, 'http://www.krkrealty.com', None, 'https://www.grizzlyssweep.com', 'http://www.health-local.com/biz/walk-in-clinics/toronto/ontario/primacy-queens-quay-medical-centre/', 'http://www.starsburgers.com', 'http://www.bonjouryallbakery.com', 'http://www.southendexchange.com', None, 'http://www.nelsonpediatric.com/', None, None, 'http://www.dallasandco.com/', 'https://www.walgreens.com/locator/walgreens-2730+broadway-lorain-oh-44052/id=10222', None, 'http://www.wildcactuscompany.com', 'https://nellislife.com/gun-club/', 'http://www.theexquisitebride.com', None, None, None, 'http://www.myfavoriteguitars.com', 'http://cheeksbarandgrill.ca', 'http://www.tgifridays.com/', 'http://www.thebritishchippy.com/', 'http://www.shell.ca/', 'http://www.mesaartscenter.com', 'http://www.patcatans.com/craft-store-locations/westlake-oh', 'http://threadslifestyle.com', 'https://www.vspa-charlotte.com', 'http://www.theteamfitexperience.com', 'http://www.susieswigs.com', None, 'https://www.triplepeaksroofing.com', 'http://meadowslivingaz.com', 'http://www.lensmill.com', 'https://www.walmart.com/store/2112/scottsdale-az/details', None, 'https://www.hilton.com/en/hotels/cakfahw-homewood-suites-akron-fairlawn-oh/?SEO_id=YELP-HW-CAKFAHW', 'http://www.antiquesugar.com', None, 'http://www.rovntechs.com', 'http://www.foodcity.com', 'http://www.almustafacatering.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.dollartree.com', 'http://www.jin-jin-chinese.com', 'http://www.kyongskincare.com', None, None, 'http://www.rapidhomeservice.com', 'http://www.analogcoffee.ca', 'http://www.jajaspa.com', None, 'http://showmars.com/', 'http://harvesthalal.com', 'https://fusion4athletes.com', 'http://www.mandyfierens.com', 'https://bigricekitchen.business.site', 'http://www.corleones.net', 'http://oilchangers.ca/oil-changes-whitby-1602-dundas-st-east', 'http://mailstoremore.com', 'https://www.frysfood.com/storeHours?store=66000130', 'http://www.restorationcharlotte.net', 'http://www.illume.life', 'http://www.smiledentalclinics.com/', '1592332533', None, 'http://www.doceremedspa.com', 'https://www.speedway.com', None, 'http://www.acehardware.com/store-details/15999', 'http://bubblerepublic.ca/', 'http://thesweetnessicecream.com', 'https://www.lifesafer.com', 'http://www.premierbaseballnv.com', None, 'http://www.patcatans.com/craft-store-locations/amherst-oh', 'https://www.southernnevadapediatriccenter.com', None, None, '1592332567', None, None, 'http://miketheplumbermatthews.com', 'http://www.therocklv.com/', 'http://barkmeow.ca', 'https://scottwasteservices.com', 'http://www.lvosmiles.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://www.visualimpactaz.com', 'http://www.piatto-novo.com/', 'http://www.stlawrencemarket.com/shopping/vendors/laboucherie.html', 'https://www1.shoppersdrugmart.ca', 'https://kleenbathrooms.com', 'http://www.muchoburrito.com/', None, 'http://www.familyaffairpetgrooming.com', '1592332614', None, 'http://www.goldenmiledental.net', 'http://www.afvexoticarts.com', None, 'http://www.pcdshop.com', 'http://www.blancdeblancbridal.com', 'http://www.sharkos.com/', None, None, None, 'https://www.pillartopost.com/hansnorr', 'http://www.svsvision.com', 'http://www.maestroautorepair.com', None, 'http://www.charleys.com', None, None, None, None, 'https://www.cubesmart.com/arizona-self-storage/phoenix-self-storage/72.html?utm_source=yelp&utm_medium=ccpc&utm_campaign=ppct', 'http://summerlinsmiles.com', 'http://sienadental.com', 'http://thebagelstop.com', None, 'http://woodstreetgalleries.org/', 'http://www.marriott.com/hotels/travel/cltep-residence-inn-charlotte-south-at-i-77-tyvola-road/', 'http://www.nextcare.com/locations/nc/gastonia/?utm_source=Yelp&utm_medium=Local&utm_campaign=gastonia', None, 'http://www.worldgym.com/cleveland-heights', None, 'http://www.raregemappraisals.com', 'https://www.pecosdental.net', None, 'http://www.sentrybox.com/', 'https://www.rmcf.com/NC/Charlotte50682', 'https://locations.theupsstore.com/pa/pittsburgh/4885-mc-knight-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.martins-nursery.com', 'http://www.restaurantmagnus.com/', None, 'http://theashleymethod.com', 'http://www.fountainoaks.com', 'http://midtownkitchen.ca/', 'http://locations.dennys.com/OH/AKRON/202063', 'http://www.noodles.com', 'http://www.bestmatt.com/', 'http://www.pizzahut.com/', 'https://tractorfoods.com', 'http://www.autowits.com', None, 'http://www.mononapizzaoven.com', 'http://www.tacos101.com', 'https://locations.jackinthebox.com/us/nc/gastonia/3618-e-franklin-blvd', 'http://www.kfc.com/storelocator/Default.aspx?address=5249+E+Brown+Rd%2CMesa%2CAZ', None, 'http://www.thelashloftoh.com/', 'http://www.einsteinbros.com', 'http://www.artisan-plasticsurgery.com', 'http://www.phoenix-comics.ca', 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', 'http://www.therecroom.com', 'http://www.saje.ca/', 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6153', 'http://www.fatfishblue.com/', 'https://www.lifetimefitness.com/spa/spa-salon.html?utm_source=yelp&utm_medium=directory&utm_campaign=PLM-acquisition', 'http://www.vcahospitals.com/mountain-view/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Mountain_View_Animal_Hospital&utm_campaign=main_url', 'http://cabalsocial.com', 'http://www.ampm.com', 'http://www.lanternrose.com', None, 'http://www.highsocietyresale.com/', 'http://www.theareparepublic.com', None, 'http://www.walmart.ca/en/toronto/3106', None, 'http://wiegandbrostransmission.com', 'http://thenicecliniclv.com', None, None, 'http://www.coachsbottleshopandgrille.com', 'http://www.piesquared.com', 'https://www.bonefishgrill.com/locations/oh/cleveland', '1592332797', 'http://www.ravenphx.com/dining-and-events/grill-36', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.thehakansgroup.com/', None, 'http://www.tonyromas.com/', '1592332813', None, 'http://www.metrogolfdome.com', 'http://www.toronto.ca/parks/prd/facilities/complex/263/', 'http://www.vegasghosts.com', None, 'http://www.electroncomputers.com', None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.vividsoulbodywork.com', 'http://www.ikonsalon.ca', 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://www.fusionhairbody.com', 'http://www.rounderslv.com/', 'http://brimellcsn.com', None, 'http://www.starvingartistbar.com', None, None, 'http://www.suvinowineryaz.com', 'http://orogoldlocations.com/portfolio/canada/', 'http://www.acrxpharmacy.com', None, 'http://www.firehouseloungepgh.com', 'https://enticare.com/deer-valley/', 'http://www.myamericanbuyers.net', 'https://shycoffeeco.com', None, 'http://www.bevmo.com', 'http://www.jitmoving.com', 'http://www.videogameconnection.com', None, 'http://www.toyauto-motive.com', 'http://beachventuresroofing.com', None, 'http://www.deltaco.com', '1592332897', 'http://www.meckabc.com', 'http://fatninjabite.ca', None, 'http://www.phoenixshuttersandblinds.com/', 'http://www.goodwill.vegas/thrift-store-74-7420-south-rainbow-boulevard-las-vegas-nv-89139/', 'http://www.navigatorsinsurance.ca/', 'http://www.scottsdaleastonmartin.com', 'http://www.georgesfamousgyros.com', 'http://www.footstepsinc.com', None, 'https://www.sonoraquest.com/find-a-location/fountain-hills-saguaro-blvd-palisades-blvd-closed-for-lunch/', 'https://www.dqrichmondhill.com', None, 'http://anwauto.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.sheetsvip.com/', 'http://www.msa-ec.com', 'http://dillensfamilyicecream.com', None, 'http://www.offthecleaver.com', '1592332944', '1592332947', 'http://www.coffeetime.com', 'http://www.badgerhomeinspections.com', None, 'http://www.westernanimalhospital.com', None, 'http://www.revolutioncarpetcleaners.com', 'http://vetrescueinc.vetsourcecms.com', 'https://local.firestonecompleteautocare.com/nevada/las-vegas/3770-s-maryland-parkway/', None, None, 'http://www.yesupnet.com', None, 'http://pureradianceaz.com', 'http://gandkautodetailing.ca/', 'http://www.sundanceballoons.com', 'https://urgentvet.com', 'http://www.justfresh.com/menus.aspx', None, 'http://thedailydetails.com', 'http://www.nailsforyoustouffville.ca', 'https://www.avilladeervalley.com', None, 'http://www.transmissionrepairhq.com', None, 'http://www.katiehaslam.com', 'http://www.dunkindonuts.com', 'http://www.whasn.com', 'http://www.tonydigiuseppemortgage.com', None, None, 'http://childrenslighthouse.com/matthews', 'http://wiseagent.com/', None, None, None, 'http://mazajhookahlounge.com', 'http://www.fantasticsams.com/', 'http://www.beararmsaz.com', 'http://paytonsbar.net/', 'http://www.sizzloz.com', None, None, 'http://maryscakeslv.com', 'https://bakethreefifty.com', None, 'http://nutrishopstore.com', 'http://www.royalvisionlv.com', '1592333055', 'https://www.sotfsupplements.com', None, 'https://www.cubesmart.com/nevada-self-storage/las-vegas-self-storage/90.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'https://www.interiordesignrockyriveroh.com', 'https://www.pizzahut.ca/#!/home', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://douglasartandframe.com/', 'http://www.smoothieking.com/location/view?store=1302', None, 'http://www.fetchingfoods.com', 'https://foothillsmontessori.com/?utm_source=Yelp', 'https://drstile.com', 'http://www.capitolbanquet.com', 'http://www.rehabplusphoenix.com', 'https://uptownsuites.com/locations/concord-north-carolina/', 'https://rvonthego.com/arizona/mesa-spirit-rv-resort/?utm_campaign=Yelp_Directory_Listing&utm_medium=directory&utm_source=Yelp', None, None, 'http://www.motoghost.com', 'http://weissguysaz.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006430432974&ds_s_kwgid=58700000444953100&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://storelocator.pepboys.com/pepboys/stores/las_vegas/east_charleston/00685', None, 'http://www.creativeparadise.com', 'http://mosaicsalonvegas.com', None, 'http://www.hairbenders.ca', 'http://www.brendascakegallery.com/', None, 'http://www.betty-bling.com', 'http://catalyst.lawyer', 'http://www.nobuofukuda.com/', 'http://www.grandluxcafe.com', 'http://omegaac.com', 'http://www.thechickery.com/', 'http://onestopjunkremoval.com', 'http://continentalhair.com/', None, None, None, 'http://carpetweaversflooring.com/contact-us/profile/champaign?utm_source=Yelp&utm_medium=Web&utm_campaign=MohawkYelpProgram', 'http://www.MountainWestDentalSpecialists.com', 'http://www.davidhancockdds.com/', None, 'https://www.sedonaridgephoenix.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.firetruckpizzacompany.com', 'https://www.funnjumpaz.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.thriveskinboutique.com', 'https://www.dentalclinicphoenix.com', 'http://fastserveaz.com', None, 'http://www.zoomoptical.ca', None, 'http://www.allanlaw.ca/', 'http://www.rjsgaterepair.com', 'http://www.fionnmaccools.com/locations/brampton-ray-lawson', None, 'http://www.riseupbakeryaz.com', 'http://www.pizzanova.com', '1592333200', 'http://www.cardinalewaymazdamesa.com/?ibp-adgroup=yx_target', 'http://www.carxpress.com/contactus.aspx', 'https://www.starbucks.ca', 'http://www.scratchculinary.com', 'http://www.thelittlegym.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280216206&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', '1592333224', 'https://www.flowersofcharlotte.com', None, 'http://paintlv.com/', 'http://www.merixfinancial.com', None, 'http://www.wirelessphonebooth.com', 'http://www.pdshred.com', 'https://locations.tropicalsmoothiecafe.com/nv/henderson/10612-south-eastern-avenue', None, 'http://www.eurogyro.com', 'http://www.RileyPools.com', None, None, 'http://dyneonavenue.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.valottastuxedo.com', '1592333262', None, 'http://7eleven.ca/store-locator/14812', 'http://www.azretrorentals.com/', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', 'https://local.fedex.com/nv/las-vegas/office-1441/', 'https://www.ihop.com/en/restaurants-pineville-nc/9940-pineville-matthews-rd-477', None, 'https://www.storquest.com/self-storage/az/phoenix/1096/', 'http://www.campbowwow.com/henderson', 'http://www.judygerbercpe.com', 'http://www.banfield.com/veterinarians/nv/henderson/hen?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://vegasthreading.business.site', 'https://www.starbucks.com/store/16004', None, 'https://www.bellelashlounge.com', None, None, None, 'http://www.kensmeatsanddeli.net/', None, 'http://www.tiffanycouturecleaners.com/', 'http://www.bombayonthelake.ca', None, None, 'http://www.publicschoolreview.com/school_ov/school_id/126841', 'http://www.concentra.com', 'http://www.scenicdrive.org', 'https://www.muchbetterplumbinglv.com', 'http://www.harryrosen.com/store/Chinook%20Centre', 'http://www.waxon.ca', None, 'https://throwaxes.com', 'http://www.kachinatea.com', 'http://www.torontocarnival.ca', 'http://www.omindianbistro.com', None, 'http://www.thesimplefarm.net', 'http://www.thaicuisineexperts.com', 'http://plomberielafleur.ca', 'http://sticktoittint.com', 'http://www.monoshealth.com/', 'https://sprayfoamengineers.com', None, 'http://www.greenbamboodelivery.com/', None, 'https://locations.wafflehouse.com/oh-willoughby-1716', 'https://www.mesquitelandscapinginc.com', 'https://www.signaturestyle.com/locations/wi/verona/cost-cutters-verona-shopping-center-haircuts-17552.html', 'https://www.jerseymikes.com/3096', 'http://www.housepaintinginchandler.com', 'https://www.kenstransmissionphx.com', None, None, None, 'http://www.pcsautobody.com', 'http://www.gregsrooter.com', 'http://www.shoelessjoes.ca/', 'http://www.toronto.ca/parks/prd/facilities/complex/433/index.htm', '1592333401', 'http://www.futureshop.ca/', 'http://www.concentra.com', 'http://www.NVeyeSurgery.com', None, 'http://castlenoel.com/', 'http://www.fatsospizza.com', 'http://www.akadogtrainingnow.com', 'http://www.timhortons.com/ca/en', 'http://www.zeldas.ca/', None, 'http://johnnyrockets.com', 'http://www.desertskygames.com', 'https://www.mayfieldfloral.com/?srccode=yelp_track', None, 'https://www.moes.com/find-a-moes/south_carolina/clover/6016?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://avantidoorgroup.com', 'http://www.beanartistaz.com', 'http://www.skinspecialistsofaz.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.baskits.com', 'http://www.lagomarsinolaw.com', 'http://www.superstarcarwashaz.com', 'http://www.fowlsfarmmarket.com', 'https://www.voodoobrewery.com/locations/cleveland', None, 'http://www.jackpotbrandz.com', None, 'https://ad.doubleclick.net/ddm/clk/434343683;236814625;k', 'https://www.urbanagardenrestaurant.com', 'http://www.greatskinrules.net', 'https://www.cellairis.com/store-locator', 'http://www.smiletodayphoenix.com', 'http://www.fourseasonscleaner.com', 'http://miyagisnoda.com', 'https://www.choicehotels.com/arizona/scottsdale/sleep-inn-hotels/az812/rates', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'http://www.drkhanujaddsmd.com', 'http://www.belfiero.com', None, 'http://www.benfranklinpress.com', 'https://www.kirklands.com/custserv/store.jsp?storeName=Concord+Mills', 'https://www.laval.ca/centredelanature/Pages/Fr/accueil.aspx', 'http://www.torontoflowergallery.com/', 'https://www.coffeebean.com/store/usa/phoenix/cave-creek-road-and-101', None, 'http://www.stardustbuilding.org', 'http://www.myfortmillfamilypractice.com', 'http://www.cynthiaschinese.com', 'http://www.nishiegs.com', None, 'http://www.kellyhawkins.com', 'http://www.machinegunbebe.com', 'http://thewinemill.com', 'http://www.waterproofpools.com', 'http://www.sinmarrealty.com', None, 'http://www.destinyrvresort.com', 'http://www.buyazforeclosures.com', None, None, None, 'http://www.greenleaflotus.com', None, 'http://www.weissguysaz.com', 'https://www.urbanbarn.com/en/stores-detail/?id=C506', 'http://romeospizza.com', 'https://www.advancedpediatricslv.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.marcelsbarandgrill.com', None, None, 'https://www.redlobster.com/locations/list/oh/elyria/6935-midway-mall', None, 'http://www.wizardworld.com/home-pittsburgh.html', 'http://teesandmore.com', None, 'http://www.teavana.com', 'https://www.mbkseniorliving.com/senior-living/az/scottsdale/tuscany-at-mccormick-ranch/?utm_source=tuscany_at_mccormick_ranch&utm_campaign=yelp', 'http://www.presotea.ca', None, 'https://www.autozone.com/locations/az/mesa/1045-s-gilbert-rd--ste-101.html', 'http://www.vitalitymedicalwellness.com', 'https://www.theboxescaperoom.com', 'http://yyc-cycle.com/', 'http://www.newfreedomproperties.vegas', 'http://www.mypettingzoo.com', 'http://www.urgentcareextra.com/location/tropicana-jones/', 'http://www.heritageflowershoppe.com/?srccode=yelp_track', None, 'https://www.long-mcquade.com/location/Ontario/Scarborough', 'http://www.internationalcheese.ca', 'http://www.torontotemperancesociety.com/', 'http://www.eatalianpasta.com', None, 'http://bossdogbrewing.com', None, 'http://www.furnitureplacelv.com', 'http://www.doggiedelightsonline.com', 'https://www.serranosnv.com/', 'http://www.theseductivelash.com', None, 'http://www.rickslasvegas.com', None, None, None, None, '1592333654', None, 'http://www.advancedhearinggroup.com', 'http://www.sliceonbroadway.com/carnegie', 'http://www.promptwindowcleaning.com', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=101357', 'http://www.pintville.com', 'http://www.bravost-lazare.com', 'http://www.arizonatshirtfactory.com', 'http://www.iconbraces.com', 'http://www.purerelaxmassage.com', 'http://www.ljsilvers.com', 'http://www.manstop.ca', 'http://www.cbac.com/gilbert-baseline?utm_source=Social&utm_medium=Yelp', None, 'http://www.townhomeshorizonridge.com', None, 'http://www.azmdlaser.com', 'http://www.MarilynVegas.com', 'http://thericegarden.com/', None, 'http://www.roysrestaurant.com/locations/NV/las_vegas.asp', None, 'http://www.oasisstreetsville.com', 'http://www.curryaway.com', 'https://www.stubbyspuboh.com', 'http://www.allmakesautorepairs.com', 'http://crysmode.com', 'https://www.hilton.com/en/hotels/phxcdhw-homewood-suites-phoenix-chandler/?SEO_id=YELP-HW-PHXCDHW', 'https://forrestanderson.net', None, 'http://www.pittmovers.com', 'http://www.laurasecord.ca', None, 'https://myhearingcenters.com/locations/nevada/henderson/', 'http://hotspotchinesecuisine.business.site', 'http://www.victoriassecret.com', 'http://sweetfacephoto.com', 'http://holycraftcleveland.com', None, 'http://www.patcatans.com/craft-store-locations/parma-oh', None, 'https://www.jerseymikes.com/9043', 'http://nailangelos.com', '1592333759', 'https://eyeinstituteaz.com', 'http://www.rossstores.com', None, 'http://www.thunderbirdobgyn.com/june-kwark-md.html', 'http://www.brickstreetbakery.ca', '1592333772', 'http://www.therebellounge.com/', None, None, 'http://www.riccisausage.com', None, None, None, None, None, 'http://www.sonorandeserteye.com/', None, 'http://www.smokersetc.com', 'http://www.mcgrathsfishhouse.com/', 'http://www.puckettsflooring.com', 'https://www.titlemax.com/store/phoenix-e-warner-az-41-title-loans/?utm_source=yelp&utm_medium=listing&utm_campaign=places&tmx_id=771c0159ac754cf&sf_traffic=paid_listing_yelp', 'http://www.greencabofmadison.com/', None, 'http://www.cluckncup.com', 'http://www.shanesribshack.com/hwy521/', 'http://locations.budget.com', None, None, 'https://www.skindeepbyvictoria.com', 'https://www.mick-usc.com', None, '1592333826', 'http://www.nicksmenswear.com', 'http://www.classactdanceandgym.com', 'http://www.azhousing.com/', 'https://www.lifemark.ca/Bridlewood', None, None, None, None, 'http://www.drrenukakumar.com/', 'http://www.drstevenghim.com', 'https://stores.golfgalaxy.com/oh/akron/3028/', 'http://www.azkidsdoc.com', 'http://www.properpittsburgh.com/', None, None, None, 'http://www.maxandermas.com', 'http://www.arraysouthmountain-apts.com', 'http://www.unionhillsdental.com/', None, 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://www.firstfriday-lasvegas.org/', 'https://www.choicehotels.com/arizona/surprise/ascend-hotels/az444/rates', None, 'http://lyndseyloveshair.com', 'https://www.newyorknewyork.com/en/restaurants/america.html', 'http://cleoandclementine.com/', 'http://www.aquanails.ca', 'http://locations.michaels.com/ON/RICHMOND-HILL/3949/', None, 'http://www.qisalon.com', 'http://www.theivyinteriors.com', None, 'http://www.auravapes.com', None, None, None, 'http://www.shawnessymedicalclinic.com', 'http://www.torontopearson.com', 'http://www.freezonelv.com', None, None, 'http://www.lapetite.com/your-local-school/henderson-nv-7302/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://nutrishoplasvegas.com/', 'http://www.gardengrovehuntersville.com', 'http://www.royalbeef.ca', 'http://www.lifeacupuncturebodywork.com/', 'http://icepanusa.com', 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'http://www.germanautoservice.com/', 'http://www.perkavenuecoffeeshop.com', None, 'http://www.blockbuster.com', 'https://dogtrainingelite.com/phoenix', 'http://www.devillecoffee.ca', 'http://www.hairartzy.com/home', None, 'https://www.mowitall.com', None, None, None, 'http://www.coronadopreppreschool.com', 'https://asaprestoration.net', None, 'http://www.comforthospicecare.com', None, 'http://landing.trugreen.com/yelp?city=Indian%20Trail&state=NC&zip=28079&utm_campaign=ORGANIC&marketingpartner=9817', 'http://swdalarms.com', 'http://www.fallstoolrental.com/', 'http://www.kindredlivingfountains.com', 'http://www.martinizing.ca', 'http://amigoslatinflavour.com', 'http://www.barhopbar.com/', None, None, 'http://www.bzdeli.com', None, None, 'http://southpointcasino.com/dining/michaels-gourmet-room?cid=ypmic', 'https://locator.bmo.com/Default.aspx?t=hb', 'http://www.vitalityfitnesscalgary.com', None, 'http://www.hairextensionscottsdale.com/', 'http://www.paciugo.com/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'http://24hrlockouts.com/lasvegas/', 'http://pizzabooyah.com/', 'https://www.amazingpianos.com', 'https://alcatrazescapegames.com/phoenix/', 'http://www.romeospizza.com', None, 'http://www.quiktrip.com/', 'http://www.itsjustlunchlasvegas.com', 'http://www.freshkabob.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://hooterscasinohotel.com', None, '1592334055', None, 'http://www.blueheel.ca/', 'http://www.drharmandentalcare.com', 'http://www.scooptacular.com/', 'http://nynyfreshdeli.com/', 'http://www.torontofamilyhearing.com', 'http://www.glamagaltweenspa.com', None, '1592334078', 'https://www.overture.org', 'http://www.valueselfstorage.com', None, 'http://www.cnjcomics.com', None, 'https://www.donutbar.com/scottsdale', 'http://www.treasureisland.com', 'http://www.spanishtime.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006616489552&ds_s_kwgid=58700000454623699&ds_e_adid=%7BAdId%7D&ds_url_v=2', 'http://www.alpost61.org', 'http://www.hollandresidential.com/talise', 'http://sunshineimports.ca/', 'http://www.attitudematthews.com', 'http://www.acasalon.com', 'https://www.surmesur.com/en-us/contact-us/pittsburgh', None, 'http://chimeragolfclub.com', 'http://www.lacanastacapitolio.com', 'http://cherryautoglassworks.com/', '1592334129', 'https://www.lvdanceacademy.org', None, 'http://www.mtnparkchiropractic.com', None, 'https://www.empirehenderson.com', None, None, 'http://www.townhallohiocity.com/', None, 'http://www.hendersonlandscapingservices.com', 'http://www.kefferhyundai.com', None, None, 'http://www.hqbeautycare.com', None, 'https://locations.cariboucoffee.com/us/nc/charlotte/4327-park-road', '1592334163', None, 'http://www.aquilis.com', None, 'http://www.gossimo.ca/acceuil', 'http://sweetlees.ca/', None, 'http://www.ace-plumbing.ca/', 'https://www.sportsexchangeaz.com', None, None, None, 'http://www.zloungepgh.com', 'http://pizzaforeverpa.com', '1592334189', '1592334192', None, None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://alfaindentistry.com', 'http://discount-locksmith-mesa.com', 'http://www.marriott.com/hotels/hotel-information/restaurant/phxno-scottsdale-marriott-at-mcdowell-mountains/', 'http://www.sugarpinesfarm.com/', 'http://www.shopjustice.com', 'https://www.petpeoplestores.com/hudson-store.html', None, 'http://www.lightingdesign.com', 'http://flooringcontractorgilbertaz.com', 'http://www.dtraz.com', 'http://www.wellsfargo.com', None, None, 'http://www.rics-yyc.ca', None, 'http://www.childrensmuseumofphoenix.org/', None, 'http://www.northvalleygymnastics.com', 'http://www.rvupgradestore.com', 'http://www.autoglassworx.ca', 'http://www.realescapegame.ca', None, None, 'http://www.nohasslegutters.com', 'http://www.yaroplumbing.com', 'http://pennhillsrental.com', None, '1592334270', 'http://www.collingphoto.com', None, 'http://www.yelp.com/events/charlotte-yelp-quirks-out-kickboxing-at-metro-fitness-51', None, 'https://myiphonedoctor.com/locations/Decatur', 'http://pineville.burnbootcamp.com/start-today', 'http://www.georgeharounidds.com/', 'http://www.lamadeleine.com', None, None, None, None, 'http://www.lvfightshop.com', None, 'http://www.archivetattoo.com', None, 'http://www.archibaldmicrobrasserie.ca', 'http://www.Bluemartini.com', 'http://www.stadiumaz.com', 'http://www.7thchakra.ca', None, None, 'http://www.lasvegaspropertymanagement.com', 'http://www.blossompure.com', 'http://www.villagejuicery.com/', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.koyajapan.com/en/home.aspx', 'http://www.summerfieldautoservice.com/index.htm', 'http://fruitpalacehenderson.cafecityguide.website', None, None, 'http://www.forgetmenotflorals.net/?srccode=yelp_track', 'https://www.ulta.com/stores/henderson-nv-1191', None, 'https://jusfruit.ca/location', 'https://www.lifestorage.com/storage-units/ohio/cleveland/44135/116-near-brook-park/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-OH-116&utm_content=website-link&howheard=IYE', None, 'http://www.azraingutters.com', None, 'http://www.fancyfaceparty.com', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'https://stores.savers.com/on/toronto/valuevillage-thrift-store-2094.html', 'http://www.qualityautoserviceandtires.com', 'https://www.mec.ca/en/stores/toronto', None, 'http://www.lvsounders.com', 'http://www.greengoddessherbsaz.com', 'https://westonford.ca', 'https://vickstires.com', 'http://southern-nevada.pauldavis.com', 'http://www.JimmyJohns.com', 'https://www.maids.com/63/?utm_source=Yelp', 'https://www.metropcs.com', 'http://crossroadsanimalvet.com/', 'https://www.cellairis.com/store-locator', 'https://www.choicehotels.com/wisconsin/madison/sleep-inn-hotels/wi178/rates', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://duopatisserie.com', None, None, 'http://www.wholeselfacupuncture.com', 'http://jeannicola.com/', 'https://az.aaa.com/agent-office-locations/az/scottsdale/aaa-scottsdale-office', None, 'http://www.theyogasanctuary.net/', 'https://www.skinvitality.ca/?src=yelp', None, 'https://www.loveyoursmile.net', None, 'https://www.braddunlapinsurance.com?cmpid=hzrf_blm_0006', 'http://www.blinkeyewear.ca', None, 'http://www.pureintentionscoffee.com', None, 'http://www.shieldsmovers.com', 'https://elementsmassage.com/scottsdale-east', 'http://www.inyahair.com', 'https://www.applebees.com/en/restaurants-stow-oh/4296-kent-road-92017', None, 'https://www.centennialfootandankle.com', 'http://www.oreillyauto.com/site/fi/storelocator.oap#currentStore', 'http://www.leoinsurancegroup.com', 'http://24hrflood.com', 'https://www.williams-sonoma.com/?cm_ven=yelp&cm_pla=yelp&cm_ite=710', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', '1592334463', 'http://www.thedojoesports.com', 'http://www.quiktrip.com', None, 'http://www.applebees.com', '1592334474', None, 'http://www.comickazi.com', 'https://actioninsurancegroup.com/', 'http://clearancewarehouse.ca/', None, 'http://www.timothyscafes.com/en/locator/', 'https://www.theglitterboxtheater.com', 'http://www.buffalowildwings.com/?utm_source=yelp&utm_medium=yelp_profile&utm_campaign=yelp_locations', 'https://www.choicehotels.com/CN280?mc=blypypaf', 'http://shoshinkanlv.com', 'http://www.big5sportinggoods.com', 'http://www.downtownsummerlin.com', 'http://www.brewgarden.com/', 'https://www.popeyes.com/store-locator/store/restaurant_83551', None, None, 'http://www.shopgeigers.com/info/downtown-cleveland', None, 'http://www.redmountainfunding.org', 'http://mbaadmin.com', None, 'http://www.dunkindonuts.com', 'https://www.williams-sonoma.com', 'http://www.midas.com/toronto/store.aspx?shopnum=9194&dmanum=857001', 'http://1865coffee.org', 'http://www.boutiquebrockart.com', None, 'http://www.3soeurs.com', 'http://www.hartigans.com/', None, None, 'http://www.wrfx.com', '1592334544', 'http://www.joythairestaurant.com', 'http://www.greatclips.com/', 'http://www.inkconnectionllc.com', 'http://www.antennamedix.com', 'http://www.pastacasa.ca', None, 'http://www.ampm.com', 'http://www.safeandsoundpiano.com', None, 'http://www.figshomeandgarden.net', 'http://www.dollarselfstorage.com/storage-locations/arizona/glendale-self-storage.php', 'http://www.polefitnessstudio.com', 'https://www.mattressfirm.com/stores/pa/wexford/mattress-stores-wexford-pa-15090-5942.html', 'https://haircutmenavondaleaz.com', 'http://www.gttdogs.com', 'http://www.a1auctionphoenix.com', 'http://www.winkinglizard.com/', None, 'http://pacini.com', 'https://www.enterprise.com/en/car-rental/locations/us/nc/indian-trail-5388.html?mcid=iyp:8368400', 'http://www.smartsecurityaz.com/', 'https://www.bootcampcle.com', None, 'http://www.peekabookidsboutique.com', '1592334601', 'https://www.cyclegear.com', 'http://mobileonsitemammography.com', 'https://barrospizza.com', 'http://www.starbucks.com/store/9298/', 'http://www.lasvegasnvappliancerepair.com', 'http://handandstone.ca/locations/don-mills', 'https://www.clearwaterarizona.com', 'http://www.inhomechiropractor.com', None, 'http://www.excelmanagementllc.com', 'http://www.mypetsbestfriends.com/', 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', 'http://www.lapalomafuneralservices.com', 'http://www.zyggyz.com/', 'https://child-care-preschool.brighthorizons.com/AZ/SunCity/boswell', None, None, 'http://americanglassaz.com', None, 'http://bigtuna.com', None, 'http://www.veloute.ca/', 'http://www.cheyennerock.com', None, 'http://www.sasscouturesalon.com', None, None, None, 'https://www.jerseymikes.com/3146', None, None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', None, 'http://www.nicksfurniture.com', 'http://local.firestonecompleteautocare.com/pennsylvania/monroeville/397-mall-circle-dr/?lw_cmp=IYP_YPC_MLP_19461', 'http://www.jubileequeencruises.ca', 'http://pittsburgh.iqescape.com', 'http://www.jcpportraits.com', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', 'http://mindbrainlv.com', None, None, 'http://www.warriorwraps.com', 'https://familydentistrypeoria.com', 'http://www.matthewsflowerboutique.com', None, None, None, 'http://www.mulberryscleveland.com', 'http://www.davidphoto.ca', 'http://www.clevelandymca.org/lakewood.html', 'http://www.rattailjimmys.com', 'http://www.7-eleven.com/?yelp=29663', None, 'http://www.bankofamerica.com', 'https://www.discounttire.com/store/az/glendale/s/1016?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.wonderlandmontessori.com', None, 'http://myeyereadings.com', 'http://www.cafecarolina.com', 'http://no1chineserestaurant.com', None, None, None, 'https://stores.musicarts.com/east-mesa', 'https://www.sheetz.com', None, 'http://www.nspadephotography.com', 'http://Www.LiveAtAvalonAZ.com/?utm_medium=listing&utm_source=Yep', 'https://www.salonblo.com', None, None, None, None, 'https://www.lvscc.com/seven-hills', 'http://vmsdata.com', 'http://www.wellements.com', 'http://www.a1autostrada.ca', None, 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6303', '1592334790', 'http://www.hootersarizona.com', 'http://www.classiccdjrofpineville.com', None, None, None, 'http://llanteracastilloaz.com', None, 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'http://www.rickstractorservicesinc.com', 'https://www.justosgym.com', 'https://www.storquest.com/self-storage/az/apache-junction/1047', None, 'http://ladylucktattooaz.com', 'http://www.penn-station.com', 'http://www.thecounterburger.com/', None, 'http://www.sleepnumber.com/?utm_source=Yelp&utm_medium=CPC&utm_term=CTA&utm_campaign=I7JtGM_9NM1h8rs-bHdNrQ&cm_mmc=Yelp-_-Yelp-_-WebsiteLink-_-I7JtGM_9NM1h8rs-bHdNrQ-904825&tag=904825', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', None, 'http://www.essenceoftranquility.net', 'https://fitfreshcuisine.com', 'http://www.discounttire.com/dtcs/makeAppointmentForStore.do?sc=NVL-12&utm_source=Yelp&utm_medium=iyp&utm_campaign=YelpIYPSA', 'http://www.tempefountainhead.com/PropertyInformation/LucysFountainheadCafe.axis', 'http://www.richcustomjewelry.com', 'http://www.thegatewaytoathens.com', 'http://www.hnd.aero', 'https://ad.doubleclick.net/ddm/clk/318369417;146857521;q?https://www.safelite.com/stores/Champaign?utm_source=yelp&utm_medium=list&utm_campaign=Addressblock&utm_content=61820_IL', 'http://www.chickensaladchick.com/charlotte-pineville', None, None, 'http://stores.lego.com/en-us/stores/ca/chinook-ctr', 'http://eyezoneoptical.com', 'http://info.tradesecrets.ca/store-list/toronto-eaton-centre/', 'http://jjbeancoffee.com', '1592334874', 'http://www.chocolatetourofscottsdale.com', 'http://www.nvdiscountnutrition.com/', 'http://ladiesoflineage.com/', 'http://www.shell.com/', None, 'http://www.libertymutual.com/maureenbenedetto', None, 'http://www.SterlingLV.com', 'http://cosmopolitanconnections.com/', None, None, 'http://bestasianmassagelv.com', None, None, 'http://www.schiffmanlaw.com', 'http://www.priorityhealthgroup.vegas', 'http://jcweldingmobile.com', 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1259', 'https://www.bobevans.com/our-restaurants/locations/56?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.zablong.com', 'http://www.spencerautorepair.com', 'http://www.nofrills.ca/en_CA/storedetail.358.html', 'http://www.menchies.com', 'http://www.hairgrowthcenters.com', 'http://www.dsw.com', 'http://www.lcbo.com', 'http://www.tamschinesefood.webs.com/', None, None, 'http://www.sharkeyscutsforkids.com/Charlotte-NC', None, 'https://www.starbucks.ca', 'http://laprima.com', 'https://www.gingerhoneyskin.com', None, 'http://www.boosterjuice.com/', 'http://www.saludbeershop.com', None, 'http://www.acookieandacupcake.com/', 'http://pawsativedogtraining.com', None, None, 'http://www.rubberstamp.net', 'https://www.vivintsolar.com/state/arizona/phoenix-solar', 'http://www.culturalgardens.org', '1592334978', 'http://www.august8.ca', None, 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=0554&s_cid=lsl0000001', 'http://7hillslanes.com', 'http://www.deltaco.com', 'http://www.acnegurulasvegas.com', 'http://www.uwsn.org', 'https://calstate.aaa.com/?=yelp_track', 'http://www.autopaintingplus.com', 'http://www.redfishbluefishcafe.ca', 'http://www.gilbertschools.net', 'http://newgenpaintinglv.com', 'http://copycatsouth.com', '1592335010', None, 'http://www.hirockside.com', 'http://www.bodywellnessmd.com', 'http://www.brueggers.com/', None, None, 'https://representatives.countryfinancial.com/monique.allan', 'http://www.azsenioroptions.com', None, 'http://www.diesel-doctors.com', 'http://www.sapphiredentalcare.com', 'https://www.prestogeorge.com', 'https://www.steaknshake.com/locations/pa-pittsburgh-park-manor-boulevard/', None, None, None, 'http://www.tbirdendo.com?cid=list_amsg_centers_yext_link_2017', 'http://farinaccipizza.com', 'http://www.localfirstaz.com/', 'http://abarcle.com', 'http://www.lavidamocha.net', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.safelite.com/stores/Avondale', 'http://capohairbarber.com/', 'http://www.messingermortuary.com/', '1592335069', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.marvelmasonry.com', 'http://www.OP83.com', None, None, 'http://www.mywirelessdoctor.com', None, 'http://HVAC.puzl.com', None, '1592335091', 'http://www.growlerspourhouse.com/', None, 'http://www.triaplumbing.com', None, 'https://www.thesicilianbaker.com', 'http://girlsbesttrend.com/', 'http://www.tomysurpriseshuttle.com', 'http://www.redstarliquors.com/', None, None, 'http://www.redbins.ca', 'http://www.lowbudgetmovers.net', 'http://www.aquachill.com', None, 'http://www.basalcoffee.com', 'http://theupsstore.ca/148', None, 'http://www.theweesmokeshop.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.fairmont.com/scottsdale/accommodations/fairmont-gold/', 'http://ceturylink.com', 'http://www.4dSono.com', 'http://www.balzacs.com/locations/up-express', 'http://www.JCPenney.com', None, 'http://www.metropolitancleveland.com', 'http://www.kiddiekandids.com', 'http://www.cottinghamchiro.com/', 'https://www.kohls.com/stores/oh/avon-464.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', '1592335160', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://locations.michaels.com/az/glendale/2763/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', None, 'http://www.frostedfrenzy.com', 'http://www.southwestseas.com/', None, None, 'https://riothousescottsdale.com/?utm_source=Yelp%20website', '1592335185', 'http://www.starbucks.com/store/15887/', 'http://www.martialartsschooloh.com/', None, None, 'http://www.theweathershack.com', 'http://www.dillards.com', None, 'https://marcodiego.wixsite.com/thevaporroom', 'http://www.arizonahairco.com', 'http://organicnailbar.ca', 'http://www.azdne.com', 'http://restolabelle.com', 'http://www.redrockwindows.com', None, 'http://www.familyvetcare.com', 'http://www.weaveadivas.com', 'https://organize-movers.business.site', 'https://www.take5oilchange.com/locations/oh/garfieldheights-126/', 'http://www.bolderimagefloors.com', 'http://www.polyclinic.ca', 'http://www.bikramyoganorthscottsdale.com/', 'http://www.jdbyrider.com/buy-here-pay-here-champaign-illinois-il105', 'http://www.torontopearson.com/Departing_to_usa.aspx', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.aestheticdentistryofscottsdale.com/', 'http://www.goldleafdevelopment.com/the-addison/', 'http://www.lamariebrowclub.com', 'https://shop.nordstrom.com/store-details/nordstrom-toronto-eaton-centre?utm_source=yelp&utm_medium=organic&utm_campaign=fls&utm_content=835&utm_channel=lcl_brand_p&sp_source=yelp&sp_campaign=fls', 'http://www.golfcartpartscompany.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Tempe-AZ-85281/723061/', 'https://www.asher.edu/locations/college/las-vegas-campus/', 'http://thelube.com/locations/wisconsin/middleton/', 'http://www.fancykafana.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044282975319&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=1', None, 'http://kellysalonaz.com', 'http://www.flopshopauto.com', 'http://arizonaunited.com', 'http://www.northwestyogastudio.com', 'http://www.richmondamerican.com/', 'http://www.gilbertprimarycare.org', None, None, 'http://az.phoenix.charmingcharlie.com/fashion_accessories_phoenix_az_68.html', 'http://3ravens.pub', 'http://www.culinaryadventureco.com', None, 'http://www.radiancemedspa.biz', 'http://www.maximamakeupschool.com', 'https://www.mattressfirm.com/stores/nv/lasvegas/mattress-stores-las-vegas-nv-89110-6882.html', 'http://www.eides.com/', 'http://www.thaimanna.com/', 'http://www.pastabrioni.com/', None, 'https://experimac.com/scottsdale-az/', 'http://papayathaiaz.com', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.hurry4curry.com', None, 'https://www.goodwillaz.org/location/san-tan/#M6R0dDLEo9FAEQVR.97', 'http://www.platinumcollisionlv.com/', 'http://www.nicolewigs.com', '1592335342', 'http://indiancurryhouseusa.com', 'http://www.thaiseasonaz.com', 'http://cliffscustomconcretellc.com', None, None, None, 'https://www.joebird.ca/the-fix-1', 'http://www.spiritloft.com/', None, 'http://www.nowthatsclass.net/', 'http://www.thewellingtonsalon.com', None, None, None, 'http://www.docberni.com', 'http://www.bananarepublic.com', None, 'http://www.belartistry.com', 'http://www.pelicanssnoballs.com/josh12345.php', None, 'http://www.almadinapizza.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.thetopdogstore.com/', None, 'http://www.bayviewvillageshops.com', 'https://frommspestcontrol.com', 'http://www.vonnwynnstudios.com', None, 'http://www.nailsbymarlo.com', 'http://www.aaalocksmithnc.com/', None, None, 'http://www.cocofrutti.com', None, '1592335422', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280216206&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://sedationdentallasvegas.com/contact/', 'http://mariages.chaletdeserables.com', None, None, None, None, '1592335442', 'http://www.classycab.com', 'http://www.lastminute-tss.com', 'http://www.planetfitness.com/gyms/las-vegas-flamingo-nv-611?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://perfectfinishcleaning.com', 'http://englishmarbleandgranite.com', None, 'http://preciseexterminatinginc.com', 'http://www.pizzahut.com/', 'http://www.studiokhroma.com', 'http://www.thelocalcharlotte.com', 'http://cantonwong3.com/', None, 'http://www.abodefineliving.com', None, 'http://www.ohiofamilypractice.com', 'http://www.checkerpoolsupply.com', 'https://eatcopperbranch.com', 'http://senkayhair.com/', 'http://www.drmowdds.com', None, 'https://myiphonedoctor.com/locations/Blue%20Diamond', 'http://willowridgeapartments-prg.com/?utm_source=yelp&utm_medium=review&utm_campaign=prg250', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.toyscubed.com', 'http://tokyogrill.business.site', None, None, None, None, 'http://www.trainermikeaz.com', None, 'http://www.seoulgardenaz.com', 'http://www.fxauto.ca', None, 'http://www.cicis.com/locations/nc-charlotte-10707-park-rd', None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.genresportswear.com', 'http://www.phx-obgyn.md/', 'http://www.tropicalsmoothiecafe.com', '1592335539', 'http://www.sunglasshut.com', None, 'https://www.planetfitness.com/gyms/jacksonville-normandy-blvd-fl-0?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.escapefromthe6.com', 'http://jacquescafe.vegas/', 'http://www.maxfitgym.com/', 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/hillcrest-hospital', 'http://the-best-handyman-service.business.site', None, None, 'http://www.studio360spinning.com', None, 'http://torvafineart.com', 'http://www.vincefowler.ca', None, 'http://terranostrajewelry.com', None, 'http://www.BeFauxReal.com', 'http://www.myronhensel.com', 'http://www.dreamteamacademy.com', 'http://scottsdalediscountframing.com/Home_Page.php', 'https://the-quarry-bar-and-grill.business.site', '1592335599', 'http://www.lowes.com', 'https://kbhpharmacy.com/', None, 'http://www.extravaganzaevents.com', 'http://www.hoeyrx.com/', 'http://www.cactusgolfcars.com', 'http://www.mallardcreekdentistry.com/', 'http://www.bucksandbows.com/', None, 'https://www.mattressplusandfurniture.com', 'http://eSMIL.com', '1592335625', 'https://littlewoodyaz.com', 'http://www.7-eleven.com/?yelp=29384', None, 'http://www.dawnfisler.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.plasticsurgeryvegas.com', 'http://nevadaeyephysicians.com', 'http://scottsdalechristian.org', 'http://www.cyclecouture.ca/', 'http://www.shapirabuilders.com', 'http://www.MetricRealtyCompany.com', None, 'http://www.heavensentchristian.com', 'http://www.platinumcarslv.com', 'http://www.buildabear.com', 'http://www.ezsmokez.com', 'http://seattle-espresso.com/', 'http://www.fiorio.com/', 'http://www.21greens.com', 'https://rightspacestorage.com/self-storage-locations/nevada/las-vegas-nv-storage-units/3043-N-Pecos-Rd/', None, None, 'http://www.thestoryoframen.com/charlotte-main', None, None, 'http://www.outdoorsmans.com', 'http://www.torontokia.com', None, 'http://www.finepoints.com', 'http://olivepress.food-places.com', None, 'https://www.starbucks.ca', 'http://www.westernreservehd.com', 'http://www.mysterymansion.com', None, None, 'http://stevesthornhill.com', 'http://ctrconstruction.com/', None, None, None, 'http://www.illinihillel.org/cafesababa', 'http://www.bergerandson.com', None, None, None, 'http://www.ihg.com/crowneplaza/hotels/us/en/madison/msnet/hoteldetail', 'https://www.longhornsteakhouse.com/locations/oh/solon/solon/5057?cmpid=br:lh_ag:ie_ch:dry_ca:LHQ121LOCURL_dt:20200615_sn:yelp_gt:solon-oh-5057_pl:locurl_rd:1032', '1592335734', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.highmarkstadium.com', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'http://www.grandpajoescandyshop.com', None, 'http://www.ealasercenter.com', 'http://www.landmarkcinemas.com/whitby', 'https://www.downeastbasics.com', 'https://www.mistybayphotography.com', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'https://eastsidelocaleatery.com', 'http://kidzpreschool.com/contact/mountainsedgeandsouthernhighlands', 'http://www.mangomaids.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, None, 'http://www.unionvilleinfo.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'http://localheroroncy.com/', 'https://www.signarama.com/az-mesa-west/stores', 'http://www.sbarro.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTBR', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://wigsamoraz.com/', 'http://www.stphillipsbakery.com/', '1592335803', 'http://nellisforcesupport.com/Dining_Facilities.html', 'http://charlotte-ballantyne.titleboxingclub.com/', 'https://stores.jcpenney.com/oh/strongsville/clothing-stores-strongsville-oh-2683.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2683', 'https://www.aboveandbeyondacupuncture.com', 'http://www.buffalobillsroadhouse.net', 'http://www.doughboyspizzacg.com', 'http://www.myharu.ca', None, 'https://www.dominos.com', 'http://www.petco.com', None, None, 'http://www.ajgraphicsandpromos.com', None, 'https://bostonmarket.com/location/glendale-az-2407/', 'http://www.fedex.ca', 'http://www.greekvillagegrille.com', None, None, None, None, 'http://www.dunkindonuts.com', None, None, 'https://www.petradesign.ca', 'https://stores.madewell.com/en/kierland-commons?srccode=X%7CPMG%7CNaturalSearch%7CLocal%7CYelp%7C298', 'https://www.canadianstage.com', None, None, 'http://www.primrosesouthgilbert.com/?utm_source=yelp&utm_medium=maplistings&utm_campaign=localmaps', 'http://www.lv-permanentmakeup.com', None, None, None, None, 'http://www.autotintinglasvegas.com/', 'http://www.pastrypalacelv.com/', '1592335888', 'http://arcadecomedytheater.com/', 'http://www.philosophysalon.ca', 'http://swimmingpoolrepairserviceinphoenix.geocentrictechnologies.com', 'http://www.icandyphotobooth.com', 'http://www.ariumlakenorman.com/luxury-apartments/huntersville/nc', 'https://fabutan.com/locations/alberta/calgary/mission/', None, None, 'http://www.fmsc.org', None, 'http://www.kuoqinails.com', 'http://www.navonapizzeria.ca', '1592335918', 'http://www.abfirm.com', 'http://www.paradisebound.ca', 'http://www.glomedspas.com', 'http://pcparamedicnc.com', 'http://www.phase1sports.com', None, 'http://www.kettlebyvalley.com', None, '1592335937', 'https://www.planetfitness.com/gyms/brampton-centennial-mall?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://www.goldenirontattoostudio.com/', '1592335946', 'https://www.wendys.com', None, 'http://www.hotchikn.com', 'http://www.palmvalleyapthomes.com', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', None, 'https://www.copperstatemoving.com', 'http://locations.daltile.com/oh/bedford-heights/235', None, None, 'http://www.theclimbingwall.net', None, 'https://www.bannerhealth.com/services/academic-medicine/banner-university-medicine-institutes/banner-university-medicine-womens-institute', 'https://www.arizonamedicalinstitute.org', None, None, 'http://www.prestigedanceacademy.com', None, 'http://www.kiehls.ca', 'http://www.hendersonhomecareassistance.com', 'http://qualitytimeclocklv.com', 'http://www.carriecerinos.com', 'http://www.stephanoslv.com', 'https://www.pacesriverapts.com', None, 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', 'http://www.sweetflour.ca/', 'https://local.albertsons.com/az/chandler/3145-s-alma-school-rd.html', 'https://www.windstream.com', 'http://www.barnyardfleamarkets.com/', None, None, 'http://www.francescascollections.com/', None, 'http://www.tailorandalteration.com', 'http://gaterepairsmobilewelding.com', 'https://www.autozone.com/locations/il/peoria/908-s-western.html', None, 'http://storelocator.pepboys.com/pepboys/stores/pittsburgh/library_road_service_center/01425', 'https://www.chick-fil-a.com/rivergate', 'http://truesalonlasvegas.com', 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', 'http://powersportsto.com', 'http://www.wickedbeautysalon.com/index.html', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.devitis.com', 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', 'https://www.mattressfirm.com/stores/az/glendale/mattress-stores-glendale-az-85308-7920.html', None, 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=cleme&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'https://www.eyelovesmiles.com', 'http://www.starbucks.com/store/14175/', None, None, 'https://locator.bmo.com/Default.aspx?t=hb', 'http://www.smarttoyota.com', 'http://www.vegaspainters.com', None, 'http://tiptopchild.com', 'http://fitnessfor10.com/locations/nevada/las-vegas/', None, 'http://www.fortyorktavern.ca', 'https://eatpokebros.com', None, 'http://www.ilashnbrows.com', 'http://www.arizonatheatre.org', 'https://redowlburgersandbrews.com', 'http://www.centurysquareluxurycinemas.com', None, 'http://xpresscuts.com', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', 'http://www.FamilyFunscape.com', 'https://www.cleanjuice.com', 'http://www.tianchinawok.com/', None, 'http://arizonanativeroofing.com', 'https://www.simplythebestac.com', None, None, None, 'http://venetiandayspas.com', 'http://www.eattalkandplaytherapy.com', 'http://heritagemontessorischool.org', 'http://www.abarepair.com', 'https://www.krispykrunchy.com', 'http://nakato.com/japanese-steakhouse-sushi-charlotte/restaurant-charlotte-north-carolina', 'http://www.sweetcakesbakery.com/', 'http://www.azenergyefficienthome.com', 'http://annofsiam.com', 'https://www.metro.ca/en/find-a-grocery/312', 'https://www.capriottis.com', None, 'http://kornerkwiklubelv.com', 'http://www.maac.com/north-carolina/charlotte/post-park-at-phillips-place?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'https://www.sukoshimart.com', None, 'http://www.myorthodontistcalgary.com', None, None, 'http://www.nicheorganicgardens.com', 'http://www.elysiumgardensflowershop.com/', None, 'http://www.valleymetro.org', 'https://locations.theupsstore.com/wi/madison/4230-east-towne-blvd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.usps.com/', None, None, 'http://www.gilelawgroup.com', 'http://onroute.ca/location/king-city/', 'http://www.gastelumandsons.com', 'http://www.stripndipchicken.com', '1592336205', None, None, 'https://stores.nordstromrack.com/us/nv/henderson/579-n-stephanie-st?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=376&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', None, None, None, None, None, 'https://www.starbucks.com/store-locator/store/8400', None, 'http://homehardware.ca', None, None, None, 'http://advancedwomenscareofpgh.com/', 'http://cleanfreakcarwash.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'https://www.supershonda.com', '1592336247', 'http://www.genocomosalon.com', None, 'http://peaceloveandzen.com', None, 'http://www.oldspaghettifactory.ca/locations/calgary', 'http://www.cilantrobarandgrill.com', 'http://www.pizzapizza.ca', 'http://www.nextcare.com/locations/az/tempe/?utm_source=Yelp&utm_medium=Local&utm_campaign=tempe', 'http://www.escondite.ca', 'http://www.comeseeme.ca', None, 'http://www.diamondbuckleadventures.com', 'http://www.afhaz.com', None, None, 'https://honorhealth.com/locations/primary-care/honorhealth-medical-group-indian-school', None, None, None, 'http://prontomoderncuisine.com', 'http://www.liscohvac.com', None, None, 'https://www.leaffilter.com/discover/?utm_campaign=Yelp_Directory-ND&utm_medium=YELP&utm_source=41DY', 'http://www.sears.ca/', 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID361', None, 'http://www.starbucks.com/store/9289/', 'https://www.pumpitupparty.com/fitchburg-wi', 'http://www.gatewaychevrolet.net/', None, 'https://www.bandafirm.com', 'http://www.zigarren.ca', None, 'https://www.dashvapes.com/markham-vape-shop-e-cigarette-e-liquid-stores/?utm_campaign=local&utm_medium=organic&utm_source=google', 'http://brownbrothersmeats.com/', None, None, None, 'http://www.nailsforyou.ca', None, 'https://www.boudoirbymiaportrait.com', 'http://www.vpilv.com', None, 'http://www.mecklenburghealthrehab.com', 'http://comicbooklounge.com/', None, None, 'https://www.vincentsoncamelback.com/vincents/index.php', 'http://republicfoodanddrink.com', None, None, 'http://www.sahanrestaurant.ca/', None, 'https://www.handy.com/yelp50cc?utm_source=yelp&utm_medium=CPC&utm_campaign=PHX-Handy-Yelp', None, 'https://www.ediblearrangements.com/fruit-arrangements?utm_campaign=StoreID559&utm_medium=Listing&utm_source=Yelp', None, '1592336376', 'https://arizonahotairballoons.com', 'http://www.dependableelectric.com', '1592336384', 'http://www.eliteentaz.com', 'http://www.totalcigars.com', 'https://eldoradosc.com', None, None, None, 'http://uptown.bellafrescocafe.com', 'http://www.zabas.com/', 'http://www.sweetiessodashoppe.com/#home', None, None, 'http://www.starnursery.com', None, 'http://www.herbalnailsspa91st.com', 'http://www.phxpdmuseum.org', 'http://www.fitbodybootcamp.com/lasvegasnorthfitnessbootcamp/', 'http://www.bellepizzelle.com', None, 'http://ilfornoairdrie.com/', 'http://prostepmarketing.com/', 'http://www.mobilemechaniclvnv.com', 'http://www.StAmandAZ.com', 'http://www.marriott.com/hotels/travel/cakam-fairfield-inn-and-suites-akron-fairlawn/', None, 'http://www.countyelectricco.com', 'http://www.thebookstoreinmedina.com', None, 'http://www.celtictrans.com', None, 'http://www.fiestamarket.ca', None, 'http://www.customcolorandcollision.com', '1592336469', None, None, None, 'http://www.vbjs.net', None, 'http://www.fergusandbix.com', 'http://beautybycarmen.weebly.com/index.html', 'http://www.nishiegs.com', 'http://www.portsoiree.com', 'http://www.customcraftedfloors.com', 'http://www.bulldogbeerandwine.com/dilworth', None, None, None, 'http://steakiesaz.com', None, 'http://www.tsmmoving.com/', 'http://www.sallybeauty.com/', 'http://www.azfootdoc.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592336515', 'http://www.desertsongmusiclv.com', None, 'https://www.starbucks.ca', 'http://www.dunkindonuts.com/', 'https://www.supercuts.com/locations/nv/north-las-vegas/redrock-commercial-center-haircuts-81949.html', '1592336530', 'http://theburritoexpress.com/scottsdale-mexican-food.html', None, None, None, 'http://potteryland.com', None, 'http://www.dollartree.com/', 'http://madmaids.ca/', None, 'http://www.expertappliancenc.com', 'http://santafeclt.com', 'http://fluno.com', 'https://www.d9brewing.com', None, 'https://www.hyatt.com/en-US/hotel/ohio/hyatt-place-cleveland-lyndhurst-legacy-village/clezl', 'http://showmars.com/locations/galleria-mall', None, None, None, None, 'http://learnmusicnc.com/', '1592336581', 'https://www.chandlervapeshop.com', 'http://www.cornerstore4u.com', 'https://www.ediblearrangements.com/stores/18332-c-bagley-road-middleburg-heights-oh-44130', 'http://www.eklecticpie.com', 'http://www.flyghtcycle.com/', None, 'http://thegoodeggaz.com/', 'http://www.chuckwallafitness.com', None, 'http://Regency-PlasticSurgery.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.azsunburst.com/home.html', 'http://lucaffe.ca', None, 'http://www.mexx.ca', None, 'https://playlivenation.com/location/arrowhead/', None, 'https://phoenix.kaisergarage.com/contact/location/', None, None, 'http://MearsMechanical.com', 'https://tidycasa.com/?utm_source=yelp&utm_medium=url-link&utm_campaign=phoenix', 'http://www.libertymovement.ca/', 'http://www.sammyspizza.com/location/las-vegas-flamingo', 'http://www.vegasmedspa.com', None, None, None, 'http://www.ace-locksmith.net', 'http://www.paradisepictureframe.com/', 'https://az-wellness.com', 'https://www.beststudioever.com/htc-of-tempe', 'http://drperrone.com', None, None, 'http://www.plumveterinarian.com', None, 'https://www.livingatentrata.com/?utm_medium=listing&utm_source=yelp', 'http://bobaboy.ca', None, 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', 'http://www.erbertandgerberts.com/locations/detail/tempe-5th-st/mine', 'https://championplumbingandrooter.com', 'http://www.fatchoylv.com', 'http://bigboyspizzaicecream.com', None, 'http://www.helix-apts.com', 'http://www.tlilyskin.com', 'http://www.stevesknows.com', None, 'http://www.torontoacupuncturestudio.com', 'http://www.dethronebasecamp.com/', 'https://stores.joann.com/oh/north-olmsted/1923/', 'https://milios.com', 'http://www.siberimaging.com', None, 'https://branches.bmo.com/ab/calgary/b0010/', 'http://www.marinecenteroflasvegas.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCAKAS', 'http://www.urbancivildefense.com/', 'http://www.romaspizzeria.net', 'http://www.bloormillvet.ca', 'http://cars.iaai.com/', None, 'http://www.globalhomeaz.com', None, 'https://gordonbiersch.com/locations/tempe/', 'http://www.documentprepaz.com/', 'http://fixbar.ca', 'https://www.azipc.com', 'http://www.hornytoadsaloon.com/', None, None, 'http://drautoscottsdale.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCBV', None, None, None, 'http://www.drnakyoungju.com', 'http://www.hamadaofjapan.com/', None, '1592336775', '1592336778', 'http://missdaisypetgrooming.yolasite.com/', '1592336783', None, 'http://www.blossom-spa.com', None, 'http://www.bellaspapickering.ca', 'http://www.truffletrolley.com', 'http://www.wendelclarks.com/', 'https://www.avanamccormickranch.com', '1592336798', 'http://www.starshinetan.com', None, None, 'http://cltdetailing.weebly.com', None, 'http://www.ksne.com/', 'http://softtouchmoving.com', 'http://www.swimhappypools.com', None, 'http://www.zoolikins.com', 'http://www.planetorganic.ca', 'http://zuberfun.com', 'http://www.eatchinakitchen.com', 'https://www.smithsfoodanddrug.com/storeHours?store=70600381', None, 'http://www.apexmassage.com', 'http://www.studiofitaz.com', 'http://bellagohomes.com/', None, 'http://www.pinoyscoffeeandboba.com', 'https://www.minisocialaz.com', None, None, 'http://www.kyjosrestaurant.com', 'http://www.curves.com', 'http://www.volumebeautybar.com', 'https://rascalhouse.com/location/maple-heights/', None, 'https://lmakeupinstitute.edu', None, 'http://www.brooklynbagels.com', 'http://www.thebristolatsunset.com/', 'http://www.myvillageyyc.com', 'http://www.culvers.com/restaurants/charlotte-nc-university-city-blvd', 'http://www.thenextlevelinc.ca', 'https://www.buylegalmeds.com', None, 'http://www.dermedix.ca/', 'http://hopehealthvegas.org', None, 'http://musclemakergrill.com/locations?state=az', 'http://www.springchinahouse.ca', 'http://www.oneintroempire.com', 'http://www.ashgrovespa.com', 'http://www.discount-drugmart.com', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://www.hificiti.ca', 'http://www.chillichickenhouse.com', 'https://locations.davidstea.com/ab-calgary-111', 'http://www.charlotteautocare.com', None, None, 'https://www.sequoiamadison.com', None, 'https://davidshamburgers.com', 'http://lavidamassagechampaignil.com/', None, 'http://www.sonomafacialsurgery.com/', 'http://www.mobilephoenixautoglass.com', 'https://ad.doubleclick.net/ddm/clk/300150309;127077036;p', None, 'http://subarudessources.ca/', 'http://www.entc.com/schroeder.html', 'http://www.buyrightautosalesaz.com', 'http://aaawisely.com/', 'http://www.saltandlightministry.org', None, 'https://www.flowersinvegas.biz/?srccode=yelp_track', 'http://shopfreshboutique.com', 'https://www.mesamiesboutique.com', 'http://www.modoyogamaple.com', 'http://goldmansdeliarizona.com/', None, None, 'http://thefamilypetclinic.com', 'http://www.robinsnestbb.com', None, None, 'http://www.juiceboxcharlotte.com', 'https://www.humangood.org/windsor', 'http://www.copperblueslive.com/phoenix/', 'http://www.azbrowacademy.com', None, 'http://www.discount-drugmart.com', 'http://www.nahoku.com/', 'http://www.fanniemay.com/', 'https://eastcourtfordlincoln.com', None, 'http://www.heroburgers.com', 'http://whiplasheslv.com', 'http://www.kelseys.ca', 'http://www.beckeragencyllc.com', 'http://www.mcnamaratennis.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.maxxproperties.com/ventana-canyon-henderson-nv/', 'http://www.meatballs.com/?page_id=29&st=PA&locid=9', 'http://Freestylemmalv.com', None, None, None, None, 'http://www.raftingsaltriver.com/', 'https://www.lullabysleepconsultant.com', 'http://www.desertvistadental.com/?utm_medium=North&utm_source=YelpEnhanced', None, None, None, 'http://www.mcgillbb.ca', None, 'http://www.anandasalon.com', 'http://mycielosalonandspa.com', 'http://brewedclues.com', 'http://www.alliedhealthandchiro.com', 'http://www.famouslastwordsbar.com', 'http://www.valens.ca', 'http://www.brakemasters.com/location/4620-west-craig-rd-north-las-vegas-nv/', 'http://www.waltercaterers.net', 'https://fatimakarahicorner.com', None, 'https://www.wyndhamhotels.com/hotel/46020?tel=18008899735&iata=00093785&cid=fe:hj:20170523:yl:pp:hjus:46020', None, None, 'http://www.hairologysalonbirkdale.com/', None, 'http://www.paulpecorella.com/', 'https://www.yourchandlerdentist.com/?utm_source=yelp&utm_medium=website', 'http://www.metrotheatretoronto.com/', 'http://www.thegetwellcenter.com/', 'http://www.mountainviewpestcontrol.com', None, 'http://www.gasnerdental.com', 'http://www.timhortons.com/', 'http://www.treasureisland.com/restaurant/18/phovietnamese', 'http://www.noble-air.com', None, 'http://trumedaz.com/', None, 'http://www.dantespizza.ca/', 'http://www.bk.com', 'https://www.nothingbundtcakes.com/bakery/nv/las-vegas-eastern?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=las-vegas-eastern_2', None, 'http://www.campustownurgentcare.com', 'https://www.hov.org', 'http://www.opendoorstudios.com', 'http://clevelandselegantaffairs.com', 'http://www.audreraephotography.com/', 'http://www.newwestlending.com', 'https://prestigecleaners.com', 'http://www.redrockpainting.com', '1592337133', None, 'http://www.neverendingchild.com', None, None, None, 'http://www.ycstrans.com', 'http://www.dosemoving.com', 'http://www.vegantacos.net', 'http://www.sherwin-williams.com/store-locator/paint-store/Phoenix/AZ/8160', 'https://www.itcu.org/about/locations/cannery', None, 'https://satruck.org', None, 'http://azpizzaglendale.com', 'https://www.vans.com', None, 'http://www.arborcareaz.com', 'http://quesupperclub.com/', None, 'http://www.greengate.ca', 'http://www.qbarandgrill.org', 'http://oomomostore.com', 'http://thickandthinbrows.weebly.com', 'http://www.meckabc.com', 'http://svpsports.ca/stores/queen/', 'http://phxwelding.com', 'https://www.discoverchampions.com/our-locations/peoria/az/001772?utm_campaign=cp-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=001772', 'https://www.wyndhamhotels.com/hotels/44831?tel=18885959874&iata=00093785&cid=fe:gr:20160201:yl:pp:gr:44831', 'http://www.salonmodinc.ca', 'http://woodfloordoctor-az.com', 'https://www.cricketwireless.com', 'http://fiveguys.com/', 'http://www.phoenixfai.com', None, None, None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXRT', 'http://www.smiles4ulv.com', None, 'http://www.expressflooring.com/?utm_source=VYRL&utm_medium=Yelp&utm_campaign=chandler', 'http://www.tuteramedical.com', 'http://www.mymacs.ca/macs-stores/ca/calgary/2000-airport-road-ne/22172', 'http://luckys1313.com', None, 'https://milios.com', 'http://www.wattelandyork.com/about-us/', None, 'https://www.walgreens.com/locator/walgreens-5742+e+mockingbird+ln-dallas-tx-75206/id=6660', 'http://azkidsgrins.com/', None, 'http://www.newconceptssalon.com', 'https://hatchtire.com', 'http://www.santanaluxuryrentals.com', None, 'https://www.nationalcar.ca/en/car-rental/locations/ca/ab/calgary-intl-airport-c5n1.html?mcid=iyp:8368400', 'http://www.affordabledentures.com/office/mesa', 'http://www.battlearchery.com', 'http://www.formaplasticsurgery.com/', 'http://www.starbucks.com/store/14123/', 'http://www.moorespoolservice.com/', 'http://benetflorentine.com', 'http://www.bigpaws.net', 'https://www.hilton.com/en/hotels/laseses-embassy-suites-las-vegas/?SEO_id=YELP-ES-LASESES', 'http://www.upmc.com/Services/senior-communities/skilled/canterbury-place/Pages/default.aspx', 'http://www.ramintherye.ca', 'http://reggaefusion.ca', None, 'http://www.azbicycledepot.com', None, 'http://www.liquordepot.ca/?utm_source=Yelp&utm_medium=Online_Listings&utm_content=Location&utm_campaign=LiquorDepot_AB_Q3_July_September_2017', 'http://www.agentlesolution.com', 'https://www.aaapaintsupply.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', '1592337304', 'https://www.thecaysatocotillo.com/?utm_source=yelp&utm_medium=social&utm_campaign=vyrl', 'http://clickserve.dartsearch.net/link/click?lid=43700006435131063&ds_s_kwgid=58700000444951711&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://seerightnow.org', None, 'http://cullyscocktaillounge.tripod.com', 'http://www.vegascrystalhealings.com', None, None, None, 'http://www.luxemedicalartistry.com', 'https://stores.bedbathandbeyond.com/Gilbert-AZ-85296-1033', None, 'http://www.affordable-ivf.com', 'http://www.seekearlylearning.org/', None, 'http://buffalowildwings.com', 'http://lvtours.org', 'http://www.lucyssweetsurrender.com/', 'http://www.anthonyvincenailspa.com', 'https://goo.gl/CxLhdU', None, 'http://www.freshii.com', 'http://www.gordoncowie.com', 'http://www.epicthriftstores.com/?q=e002', 'http://www.InvitationHomes.com', None, 'http://www.azbiltmoregc.com', 'http://www.davisortho.ca', 'http://www.econrads.com', '1592337375', None, None, None, 'http://canpar.com', 'https://hendersonoralsurgery.com', None, 'https://lernerandrowe.com/?utm_source=Yelp', 'https://www.magnotta.com', 'http://www.pandaexpres.com', None, 'http://www.mattress360.net/', None, 'http://www.pakmailsuperstore.com', 'http://www.kmart.com', 'http://www.venusvictoriaspa.ca', None, 'https://www.hilton.com/en/hotels/cleucdt-the-tudor-arms-hotel-cleveland/?SEO_id=YELP-DT-CLEUCDT', None, 'http://www.spoonandfork.ca/', 'http://www.sincitylashes.com', None, 'http://www.cabinetsbydesignaz.com', None, 'https://www.sinfulsweetspgh.com', 'http://www.coldstonecreamery.com/stores/21246', 'https://www.pepperbox.co', None, None, None, None, 'http://www.arizonahairco.com/', 'https://www.dieselspecialistsinc.net', '1592337450', None, None, 'http://www.azadventures.com', 'http://www.JimmyJohns.com', 'https://hikeprint.com', 'http://www.pinballshoppe.com/', None, None, 'http://www.hackneyairconditioningandheat.com', 'http://www.johnnyrockets.com', None, 'http://www.americanfreight.com/?utm_source=yelp&utm_medium=social&utm_campaign=profile', 'https://www.zaxbys.com/locations/sc/clover/143-highway-274/', None, 'http://www.dreamcurlssalon.com', None, 'http://www.pizzadepot.ca', 'http://www.banfield.com/veterinarians/nv/las-vegas/smm?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.dapaolotrattoria.com', 'http://www.portofinoseniorapartments.com', 'https://buenavistakitchen.com', 'http://www.borrel.ca', None, 'http://www.bk.com', 'https://www.2020visioncarepgh.com', 'http://www.goodwill.vegas/thrift-store-68-4580-west-sahara-avenue-las-vegas-nv-89102/', 'http://www.sweatshopunion.ca', 'http://pettycashtoronto.com', 'http://www.zappysautowashes.com/', 'http://www.101bottles.com', 'http://bogartspet.com', 'http://www.starbucks.com/store/9298/', None, 'https://www.wyndhamhotels.com/hotel/13164?tel=18008899735&iata=00065402&cid=fe:hj:20170523:yl:pp:hjca:13164', 'http://portraitstudio.com/location/3001/AZ/Tempe/85284/Walmart-Supercenter---#1746', 'http://euvori.com', None, 'http://www.goretailgroup.com', 'http://www.copemanhealthcare.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281379818&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'https://www.thetenspot.com/yonge-eglinton', None, 'http://www.fullglamsalon.com', 'http://www.upmc.com/locations/hospitals/Magee/OBGYN/Pages/default.aspx', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', 'http://www.restaurant-mysore.com', None, 'http://www.thewineloftpittsburgh.net', None, 'http://www.dechance.com', 'http://chase.com', 'http://www.foothillsinsurance.com', None, 'http://www.aspendent.com', 'http://eyedentitylv.com/', None, 'http://seasontreeservice.com', 'http://www.hihealth.com', 'https://www.anytimefitness.com/gyms/2127/McMurray-PA-15317/?utm_source=yelp&utm_medium=local', 'https://www.pbteen.com', 'http://stratusrestaurant.com/', None, 'http://www.jasperspeakbistro.com', 'http://www.hampton-pa.org/Facilities/Facility/Details/Hampton-Community-Park-2', 'http://www.missionecommerce.com', None, None, None, None, 'http://www.propassportphoto.com', 'http://www.saintmarysbasilica.org', 'http://www.brunos.ca', 'http://www.starbucks.com/store/11823/', None, 'http://www.urodoc.net', None, None, None, None, 'http://www.puredentallv.com', None, '1592337639', 'https://www.giannasbestpizza.com', 'http://brewsters-cbp.com', 'http://www.doggieplayland.ca', 'https://www.mynewimagesmile.com/contact/glendale/', 'http://www.parrotdiseperch.com', 'https://nathansfamous.com/restaurants/luxorhotelcasino-lasvegas-130416/', 'http://www.videoaudiospecialists.com', 'http://www.childrensdentalvillage.net/', 'http://www.24-7jbservices.com', 'http://www.barkbusters.com/dog-training-las-vegas', None, 'http://www.jeenanails.com', 'http://www.waterfrontoronto.ca/explore_projects2/east_bayfront/canadas_sugar_beach', None, 'https://parsleymediterranean.com', None, 'http://www.sonamesthetictouch.com', None, None, None, 'http://www.timhortons.com/', None, None, 'https://www.harveys.ca', None, 'http://www.wmvaz.com', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://www.bk.com', '1592337708', 'http://www.fourseasons.com/toronto/dining/avenue.html', 'http://www.regency.edu/campus/charlotte/?guest', 'https://www.restaurantszibo.com/les-restos/anjou', 'http://www.twistbyoliver.com', 'http://www.classicopizza.com/', 'http://www.bjs.com', None, 'http://www.spayaz.com/locations/cleveland-oh/', 'http://www.cheznanoumadison.com', None, None, 'http://www.saq.com/webapp/wcs/stores/servlet/SAQStoreLocatorSearchResultsStoreDetailsView?storeLocationId=10233&catalogId=50000&langId=-1&storeIdentifier=23337&storeId=20002', 'http://baristacafeaz.com/', None, 'http://www.fhcs.net', 'http://southernaccentexpress.com/', None, None, 'https://www.victoriassecret.com', None, 'https://auctionnation.com/locations/glendale/', 'http://www.mountedimage.com', '1592337761', 'http://robertlangford.com', None, 'https://www.pentagonplumbinginc.com', 'http://www.littledevilcupcakery.com', None, None, None, 'https://www.chick-fil-a.com/arboretum', 'http://www.papamurphys.com', 'http://www.azwaterdamageexperts.com', 'http://www.A1dvancedServices.com', 'http://thevillagediner.com', None, 'http://www.idealenergyaz.com', 'http://www.K-9Behave.com', None, 'https://www.heinens.com/Heinens-of-Aurora', 'http://www.westernfundinginc.com/', 'http://www.rexglass.com', 'http://www.cambriagilbert.com', 'http://www.doggiestayedhome.com', None, 'http://hwy55.com', None, None, 'http://www.murrysvilleautoclinic.com', 'http://www.toolboxdancestudio.com/', None, 'http://sycamorebrew.com', 'http://www.fastfreshfoods.ca/', 'https://www.sprint.com/storefronts/bd/sprint-surprise-az-85388-d-8981/', 'http://www.fiorio.com/find-a-location/gibsonsquare/', 'https://www.santandental.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'https://www.fishwindowcleaning.com/akron/', None, 'http://www.aria.com/', None, 'http://www.smoothieking.com', 'http://www.bobbywestpgh.com', 'http://www.guildmortgage.com/officers/kevinhelm', None, None, 'https://honeypotwaxspot.com', None, None, 'http://www.thespokeclub.com', None, 'http://www.creosoteaz.com', 'http://www.grossmanstavern.com/', 'http://www.lucullusbakery.com', None, 'http://www.1065.com', 'https://glassnickelpizza.com/location/fitchburg/', 'http://downtowntattoo.vegas', 'http://www.thestoreonqueen.com/', None, 'http://www.otakumen.com', '1592337898', 'http://www.cswellnesscenter.com', 'http://www.emeraldnecklaceinn.com', None, 'http://www.embassysuitesconcord.com/caffeinas-marketplace-cafe/', 'http://www.ipaverdesign.com', None, 'http://globalpi.com/', None, None, 'https://www.potterybarnkids.com/?cm_ven=yelp&cm_pla=yelp&cm_ite=573', 'http://yyz.millstreetbrewpub.ca/', None, 'http://2themaxsalon.business.site', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', 'http://designsbychrista.net', 'http://www.twisted-fork.ca', None, 'https://www.thebrick.com/pages/store-richmond-hill', 'http://www.framinworks.com', None, None, None, None, 'https://merakihairandbody.com', 'https://www.mypaintedtrailsapts.com', 'http://www.worksburger.com/Locations/Toronto-The-Beach.aspx', 'http://www.goodlifefitness.com', 'http://azbesthomecare.com', 'http://goodtasteshanghaicuisine.com/', 'https://www.clevelandmetroparks.com/zoo/programs-events/2018/special-events/asian-lantern-festival?gclid=CjwKCAjwy_XaBRAWEiwApfjKHoqvP1jO52KiXgjdBVa76aZomBnBV1xmTTlKINKJWcWsTw5zw-uNHhoC3KMQAvD_BwE', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.staples.com', 'http://www.barematters.com', None, None, 'http://www.centreduvernay.ca/home/', None, None, 'https://pizzanova.com/pizza-nova-vaughan-9960-dufferin-st/', 'http://www.ntb.com/store/8546/monroeville-pa-15146-2601?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'http://captainkookoo.com', None, 'https://ad.doubleclick.net/ddm/clk/434319861;236814625;l', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.simons.ca/fr/magasins/laval--a13200', None, 'https://www.longhornsteakhouse.com/locations/in/avon/avon/5157?cmpid=br:lh_ag:ie_ch:dry_ca:LHQ121LOCURL_dt:20200615_sn:yelp_gt:avon-in-5157_pl:locurl_rd:1117', 'http://www.starbucks.com/store/11425/', 'http://www.prantlsbakery.com', None, 'http://www.oolonghouse.com', 'http://www.theboilingharbour.com', 'http://cowtownrange.com', None, 'http://thebarberyaz.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, 'http://www.thebiltmorestudio.com/scottsdale', 'http://Www.uhaul.com', 'https://rushbowls.com/charlotte', 'https://locations.tropicalsmoothiecafe.com/pa/moon-township/9898-university-boulevard', None, None, 'http://ebjtouchofclass.com', 'http://angelsnails.net/', 'http://www.packshipandprint.com', None, 'http://www.dollartree.com', 'http://azprecisionpest.com', None, 'http://www.crushwinebar.com/', 'http://knockkneedlobster.menutoeat.com', 'http://atlastacatering.com', 'http://fitnessfactorycharlotte.com/', 'http://www.monkeymagoos.com', 'http://gnslasvegas.org', 'http://www.valuevillage.com', 'http://www.basinwhite.com', 'http://www.ginnyswashhouse.com', 'http://www.sherwin-williams.com/store-locator/commercial-paint-store/Las%20Vegas/NV/8237', None, 'http://www.miabellasalonandspa.com', None, 'http://www.tjonesaz.com', 'http://www.thecanadianpiecompany.com/', 'http://oasisvape.com/', None, 'http://www.cameleonhairandnailsalon.com', 'http://www.theskinandcompany.com', 'http://www.phoenixmedspa.ca', 'http://myscottsdalechiropractor.com', None, 'http://www.spamassageforyou.com', 'https://www.ontario.ca/page/serviceontario', 'http://www.dolcecasatile.com', 'http://www.zombiconjure.com', None, None, 'http://www.petpointe.ca/', 'http://www.laserepilations.com/', 'http://percywatersflorist.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.winghouseandsportsbar.com/', 'http://www.marcanthony.com/salons/', 'http://www.davidrobertagency.com', 'https://wildflowercollectivelv.com', 'http://www.seethequeen.com', None, 'https://petvalu.com/location/2169', '1592338161', 'http://www.paccana.com/', 'https://www.samsclub.com', 'http://www.searsauto.com', 'http://www.bramptonprocessservers.com/', 'http://bloomdispensary.com/bloom-dispensary-phoenix/', None, 'http://www.maidright.com/greater-phoenix', 'https://kiloguns.com', '1592338185', 'http://www.thelugos.com', 'http://www.biltmoreent.com', None, None, 'http://www.robbiesbbq.com', None, 'https://www.missionrockresidential.com/apartments/nv/las-vegas/alicante-apartments/', 'https://www.ulta.com/stores/phoenix-az-108', None, 'http://www.labocabarrio.com', 'https://www.tommyguns.com/ca/location/airdrie-sierra-springs', 'https://sunblocktinting.com', 'http://www.ubreakifix.com/locations/phoenix', None, 'https://enlytenenergy.com', None, 'https://www.rmcf.com/OH/Lyndhurst50763', 'http://www.tux-xpress.com/', None, None, '1592338229', 'http://www.gotturflasvegas.com', 'https://locations.bucadibeppo.com/us/az/peoria/16091-n-arrowhead-fountains-center-dr', 'http://www.manpower.com', None, '1592338239', 'https://www.dairyqueen.com/us-en/locator/Detail/?store-id=13912&localechange=1', 'http://uniqueluxurycatering.com', None, None, None, 'http://www.chapters.indigo.ca', None, 'http://popeyeschicken.ca', 'http://thevegitaliano.wordpress.com', None, None, 'http://www.kleinsfloral.com', 'http://www.starbucks.com/store/14175/', 'http://www.chaparralsuites.com/dining-en.html', 'http://www.broestlwallis.com', None, 'http://www.bathandbodyworks.com', 'http://www.campus.ink', 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', 'http://www.canalaz.com', 'http://freshwasabisurprise.com', 'http://websterradiator.com', 'http://mississauga.crookedcue.ca', 'http://www.ccjabersauto.com/', None, 'http://www.sudfrancedesign.com', 'http://perfectlypoochy.com', None, 'http://locations.jambajuice.com/ll/US/AZ/Gilbert/1555-N_-Gilbert-Rd_*', None, 'http://www.riodentalcentre.com', 'http://www.oceangrillmadison.com', 'http://www.pumpernickels.ca', None, None, 'http://offthehookmeatshop.net', 'https://www.caesars.com/flamingo-las-vegas/things-to-do/bird-bar?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=BirdBar&utm_content=bar', None, 'https://www.onestopmobility.com/phoenix/', 'http://phoenixk9trainers.com', 'http://chouskitchen.com', 'http://www.aldoshoes.com', 'http://www.reginospizza.com', 'http://saveyourdairy.com', None, 'http://launicarestaurants.com', 'https://rottngrapes.com/the-onyx/', None, 'http://www.keymanengravables.com', 'http://www.clothesmindedaz.com', None, None, 'http://www.shamrockbros.com', None, None, '1592338375', 'http://www.comporium.com', None, 'http://oxfordmarketpittsburgh.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.cycle-solutions.com', 'https://www.cubesmart.com/arizona-self-storage/chandler-self-storage/2.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'http://www.mindovermetalaz.com', None, None, None, None, 'http://philthyphillys.com', None, 'http://www.philthyphillys.com', None, None, None, None, 'http://www.surpriselock.com/', 'http://www.beautiologysalon.com', 'https://www.amazinglashstudio.com/studios/az/phoenix/desert-ridge-marketplace', None, None, 'http://room16pgh.com', 'http://www.afloralexpression.biz', 'http://www.epikourion.ca/', 'http://www.rocknhorsesaloon.com', 'http://www.madcatpets.com', 'http://www.moonvalleypediatrics.com', 'http://accountant-lasvegas.com', 'http://storelocator.staples.ca/stores/en_CA/ON/Etobicoke/12', None, 'https://pickettpaintingllcveronawi.com', 'http://www.kolttonfox.com', None, 'https://www.mrautosalesinc.com', None, 'http://www.kibosushi.com/locations', 'http://www.kfc.ca/store/27-ruth-ave-brampton', 'https://www.walmart.com/store/1464/charlotte-nc/whats-new', 'http://www.pizzapizza.ca', None, 'http://www.mattressfirm.com', None, 'http://www.shell.com', 'https://www.trekbikes.com/us/en_US/retail/madison_east/', None, 'http://www.shawarma-palace.com', None, 'http://okuyoga.com', 'http://www.nolandefenseattorneys.com/?npcmp=dir:local:5047293:85204', 'https://medmen.com/stores/las-vegas-spring-valley-s-rainbow-blvd-and-w-post-rd/', '1592338504', 'http://beapaintmonkey.com/', 'http://boardroomrestaurant.com', 'http://www.deandeluca.com', '1592338514', 'http://woofpetgrooming.com/', None, 'http://www.labcorp.com', 'http://www.hofstetterlandscaping.com/', 'https://federicosmexicanfood.com', None, 'https://www.trianglepest.com/pest-control-charlotte', 'http://www.hyperadvantage.com/laila/', None, None, None, 'http://www.chrishutchphotography.com', None, 'http://www.lyfekitchen.com/locations/nv/henderson', None, 'http://mrgreek.com/mrgreek.com/bathurst', 'http://www.conceptembroidery.com', None, None, 'http://www.ventureoutvegas.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://froyonayogurt.com', 'http://www.safatikka.com', 'http://www.treesonwheels.com', 'http://stationcasinospoker.com/casinos/red-rock.php?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', 'http://accentcabinetryandflooring.com', 'http://www.omsphx.com', 'http://www.arbys.com', 'http://www.thevandalpgh.com/', 'http://www.osbornejewelersinc.com', 'https://www.wellsfargo.com', '1592338589', 'https://www.5starhelicoptertours.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.spiritbarwellness.com', None, None, 'http://www.nationalglassandmirroraz.com', None, 'http://www.zappitellifinancial.com', 'https://www.blossombasket.com/about/', 'https://www.dolphingaming.ca', None, 'http://www.denmanrealty.com', None, None, None, 'https://www.hov.org', 'http://Zales.com', 'https://www.walmart.com/store/387/chandler-ok/whats-new', 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', 'http://www.adamslocksmithaz.com', 'https://www.gerbercollision.com/locations/tempe-priest-dr-az', 'https://www.bellavitaboutiquespa.com', 'http://crowelawfirm.net/west-location/4340005', None, '1592338653', None, 'https://risasdental.com/find-a-location/south-mountain/?utm_campaign=LocationPage&utm_medium=SouthMountainYelpWebsite&utm_source=Yelp', None, '1592338660', None, 'http://www.famousfootwear.com/?partnerid=YELP', None, 'https://www.emeraldwindshoney.com', 'http://frankstransmissionsinc.com/', None, 'http://pigstykids.com/', 'https://totalbodylasermedspa.com', None, 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', 'https://www.dollarplusdc.com', None, 'http://www.desertridgefp.com', None, 'http://www.yourtimemedi-spa.com', 'http://www.cmdautorepair.com', 'http://www.architecturaljustice.com/medina-design-center', 'https://ca.tokyosmoke.com/pages/queen-west', 'http://www.4lakesdrivingschool.com', 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', None, None, 'http://www.aaronbrothers.com/', None, 'http://www.libertycommons.ca', 'https://www.maxxproperties.com/remington-canyon-henderson-nv/', '1592338728', None, 'http://www.primpthesalon.com', 'http://baijialaotang.com', '1592338740', None, 'http://www.planetfitness.com/gyms/las-vegas-flamingo-nv-611?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://bodyrevive.ca', 'http://hawleycollision.com', 'https://elsupermarkets.com/las-vegas-1255-s-lamb-blvd-nv-89104/', 'http://www.uumcdc.org/', None, 'https://www.bladedbybritt.com', 'http://www.sugarfactory.com/', 'https://stores.nordstromrack.com/us/az/tempe/1900-east-rio-salado-parkway?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=150&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', 'http://www.metroinstitute.com', 'http://www.elietahari.com', None, 'http://www.paganellisbarosteria.com', 'http://qshawarma.com', None, 'http://mistersparkycharlotte.com', 'http://www.questdiagnostics.com', None, 'https://www.moes.com/find-a-moes/ohio/euclid/6468?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'https://www.bernsteinpediatrics.com', 'https://www.cosmopolitanlasvegas.com/contact', 'http://www.greulichsautomotiverepairsurprise.com', 'http://www.dunkindonuts.com', 'http://los-cedros-mexican-restaurant.business.site', None, None, 'http://www.AAACCLV.com', None, 'https://www.cuwest.org', 'http://www.thecitydinercle.com', 'http://www.big5sportinggoods.com', 'http://www.paloverdeanimalhospital.com', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, 'http://www.morgansplaceonthesquare.com/', 'http://www.SinCityGarage.com', None, 'http://2goodplumbers.net', 'http://www.5krundead.com/las-vegas.html', 'https://www.modernacupuncture.com/arizona/scottsdale/north-scottsdale-az000', 'http://tix4tonight.com', 'http://stlouiswings.com', None, 'http://www3.hilton.com/en/hotels/ontario/hilton-mississauga-meadowvale-YYZMOHH/index.html?SEO_id=YELP-HI-YYZMOHH', None, 'https://arrowheadhealth.com/locations/surprise-sun-city', None, 'http://www.rainbowgardenslv.com', 'http://jackychanvegas.com', 'http://winkinglizard.com', 'http://www.thealleycat.com', 'http://www.warmheartspet.com/', None, 'http://www.brownes.com', 'http://www.drsperbeck.com/', 'http://www.mackeyfamilypractice.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYCCR', 'https://www.torontomatchmakers.ca', 'http://www.ymcacharlotte.org', 'http://www.moltabellapizza.com', '1592338897', 'http://bornandraisedlv.com/', None, 'http://www.wildwingrestaurants.com', 'http://www.knighttutoring.com', 'http://www.levelredboxing.com/pittsburgh', None, 'http://www.brookstone.com', 'https://luvs-furries-pet-care.business.site', 'http://www.thesaabspecialist.com/', 'http://www.bradstoys.com', '1592338923', 'http://lcaecc.com', 'http://www.clarksusa.com', None, 'http://cfo.cityofcf.com/web/parks-and-recreation/natatorium', 'http://www.sushikanda.com', 'http://www.arizonawebhomes.com', 'http://www.caketini.com', '1592338944', 'http://wokbox.us/storeaz03', 'https://www.starkwaxcompany.com', 'http://www.homesense.ca', None, 'https://ride-ez.com', 'https://excellent-carpet-cleaning.business.site', 'http://www.victoriasmansion.com/', 'http://www.santosflowers.com', 'http://www.tph.ca/print/toronto-yonge-st-eglinton-ave', 'http://www.pinnaclerestore.com', 'http://www.fontanellarestaurant.com/', 'http://www.spocars.com/', 'http://www.barefootsanctuary.com/', None, 'http://yaksfitness.net', 'https://www.sinickfamilydental.com', 'http://www.mermaidcafemadison.net', 'https://www.lifestorage.com/storage-units/ohio/cleveland/44135/116-near-brook-park/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-OH-116&utm_content=website-link&howheard=IYE', 'https://www.myatlanticstorage.com', 'http://slothrecords.wordpress.com/', 'http://www.greekolivesrestaurant.com/', 'http://www.barbiesgrill.com/', 'http://ajisports.com', 'http://www.rlvdrywallandpaintinginc.com', 'http://massagebyleanne.fullslate.com', '1592339008', 'http://www.bareestheticslv.com', 'http://www.kewbeachvets.com', 'http://www.wowpatisserie.com', 'http://www.domanauto.com', 'http://www.sleepcountry.ca/', None, None, 'http://eatwalnut.com/bridgeville-pa', 'https://immaculaterestoration.com', 'http://dalmemprofessionalservices.com/', 'http://www.clevelandautomotiverepair.com', 'http://www.azpiano.com', 'http://beautybybrenda.net', 'https://locations.jackinthebox.com/us/az/goodyear/520-n-estrella-pkwy', 'http://www.eatpho.me', 'http://www.DoveValleyAH.com', None, 'https://stores.jcpenney.com/oh/mentor/salon-mentor-oh-1816.html', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=12538&localechange=1', 'http://www.unisteer.com', None, 'http://www.papajohns.com', 'https://dannysfishandchips.weebly.com', 'http://2020lasvegas.com', None, 'http://www.simplyyummybakery.ca', 'http://www.salonofscottsdale.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, None, 'http://www.cccaz.org', 'https://gpbikes.com', '1592339234', 'http://www.starbucks.com/store/15887/', None, 'http://www.shanesribshack.com', 'https://felicityanddesign.com', 'http://www.YourVegasRealtors.com', 'http://www.starbucks.com/store/14175/', 'https://www.sprouts.com/stores/details/-/store-details/view/store/6/?utm_source=yelp&utm_medium=listing&utm_campaign=website', None, 'http://lamirage.info', 'http://www.pearlconventioncentre.com/', 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', None, 'http://www.sheetz.com', 'http://www.presotea.ca', 'http://www.stainmasterslv.com/', None, 'http://www.maruspizza.com/', 'http://www.redmountaincleaners.com', 'https://www.thewalkingcompany.com/shoe_store/292/nv/las_vegas/fashion_show_mall', 'http://www.themilleateryanddrafthouse.com', 'http://www.primaryeyecenter.com', 'http://samuraimotorslv.com', None, 'http://www.middletonjewelers.com/', 'http://www.noahsnaturalfoods.ca', None, 'http://www.wsmaa.com', 'https://villageliving.org/village/', 'http://www.einsteinbros.com', 'http://www.senzaglutenfree.com', 'https://www.movingcompanybrookparkoh.com', '1592339326', 'http://www.starbucks.com/store/12233/', 'http://www.bondars.com/', 'http://www.totalwine.com/store-info/north-carolina-charlotte-myers-park/605', 'http://www.healthysmilesaz.com/', 'https://www.chick-fil-a.com/scottsdale101', None, 'http://whasn.com/locations/whasn-summerlin', 'https://www.enterprise.com/en/car-rental/locations/us/nc/huntersville-535g.html?mcid=iyp:8368400', None, 'http://urbancraftrestaurant.com/', None, '1592339359', 'http://www.el-farol.com', None, 'http://www.vistanciaanimalhospital.com', '1592339371', 'http://www.sportsbarvaughan.ca', '1592339379', 'https://locations.panerabread.com/az/scottsdale/8777-n-scottsdale-rd.html', 'http://luckypuplv.com', 'http://www.destinyhairdesigns.com', 'http://lkenviro.com', 'https://www.ihg.com/redirect?path=hd&brandCode=cv&hotelCode=lascv&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'http://www.theramed-massage.com', None, 'http://nanobrewcleveland.com/', 'http://www.springchinahouse.ca', None, None, 'https://www.simpsonpropertygroup.com/apartments/charlotte-north-carolina/promenade-park-ballantyne', 'http://www.doremischool.com', 'http://www.evolvemassagellc.com/', 'http://www.rumrunnerssaloon.com', 'http://www.skoah.com/?utm_medium=social&utm_source=yelp', 'http://vcacanada.com/crowfoot', 'https://www.theplatinumhotel.com', '1592339432', None, 'http://www.kiddiekandids.com', 'http://azbestplumbing.com/', None, 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', None, 'http://www.hotrockspa.com', None, 'http://www.scubaviews.com/', 'http://www.premiercardiovascularcare.com', None, 'https://www.verdeapartmenthomes.com', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.cleancenter.com', 'http://www.mulmerservices.ca/', 'http://www.luxesalonstudios.com', 'http://www.madrasrestaurant.ca', 'http://www.Bryantmasonry.net', None, None, 'https://creativespacesbykb.com', None, 'http://www.osteria100pittsburgh.com/', 'http://www.subway.ca', None, 'http://www.hightechappliance.ca', 'http://www.showermewithlove.com', None, 'https://locations.vitaminshoppe.com/pa/homestead/vitamins-supplements-homestead-pa-427.html', 'http://mashumashu.ca', 'http://www.scottsdalegymnastics.com', 'http://locations.arbys.com/us/pa/pittsburgh/4810-mcknight-rd.html', '1592339508', 'https://www.publicstorage.com/arizona/self-storage-phoenix-az/85027-self-storage/1113?pid=wyelp&CID=1245&CHID=AFL', 'http://go2sakura.com', 'https://www.unlimitedcollisionaz.com', None, None, 'http://www1.toronto.ca/wps/portal/contentonly?vgnextoid=a7b9dada600f0410VgnVCM10000071d60f89RCRD', 'http://www.superstarcarwashaz.com/fullservice.php', 'http://www.anthropologie.com', '1592339531', '1592339534', 'https://www.dominionselfstorage.net/self-storage/az/chandler/dominion-self-storage-chandler/', 'http://www.auntieannes.com/', 'http://www.xraymagic.com', None, 'http://www.goodwillsocal.org/', 'http://www.pizzanine.com/las-vegas', 'http://www.am2pmcarpetcleaning.com', None, None, 'http://www.mattressfactoryinc.com/', 'http://www.silverstatecu.com', None, '1592339561', None, 'http://mesacemetery.com/', 'http://www.wesellnevadarealestate.com', 'http://www.torontopaintstore.com', None, 'http://www.mygym.com/ahwatukee', 'https://ashleyhomestore.ca/pages/scarborough', 'http://www.airfitnow.com', 'https://branches.easyfinancial.com/on/branch-2501/', 'http://www.thecollectiveraw.com', None, 'http://www.circlegroofing.com', None, None, 'http://www.thehighlands-apartments.com', 'http://gleasonfamilydentistry.com/', 'http://www.sistersbuffet.com', 'http://www.group15realestate.com', 'http://www.shafferandsons.com', 'http://www.crossfitfullstrength.com/', 'http://lasvegasweddinggownspecialists.com/', None, 'https://choiceonetax.com', '1592339619', 'http://local.firestonecompleteautocare.com/north-carolina/concord/378-george-w-liles-pkwy-nw/?lw_cmp=IYP_YPC_MLP_357171', 'http://www.starbucks.com/store/9298/', 'https://rv.campingworld.com/dealer/las%20vegas-nevada', 'http://dentalnowvegas.com/', 'http://www.clubmonaco.ca', None, 'http://www.tkdaz.com', 'http://www.rexall.ca/', 'https://www.serviceking.com/locations/service-king-san-tan', 'http://www.drblackstone.com', 'http://www.simplypurelv.com/', None, 'https://www.excalibur.com/en/amenities/the-spa-at-excalibur.html', 'http://www.hailed.ca', 'http://dilworthpackingcompany.com/', 'http://www.fourthwardbreadco.com', 'http://www.hairdollz.com', 'http://www.souvia.com', 'http://aaronlelahjewelers.com/', 'https://www.trulycarpet.com', 'http://www.cookdentalmesa.com', 'http://www.lspgh.com', None, 'https://www.walmart.com/store/1895/fairlawn-oh/whats-new', 'http://www.yumtum.ca', None, '1592339686', 'http://www.tradervicslv.com', 'http://www.globalteamart.com/', None, None, 'http://www.sewickleybridgeside.com', 'http://www.ecignificance.com', None, 'http://www.laurajworley.com', None, None, 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreID=925', 'http://www.falconbeer.beer', 'http://queencitypartycharters.com/our-vehicles/', 'http://www.safeandreliablelimos.com', 'http://rainbow-cleanersaz.com', 'http://www.iRepair.ca', 'https://www.sancoffeeroom.com', None, 'http://www.tumbleweedstainedglass.com', 'http://rushintowing.com', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://www.einsteinbros.com/', 'http://www.rossdentalcenter.com', 'https://cemexconstruction.com', None, 'http://www.marcatrattoria.ca/marcawhitby', None, None, 'http://www.tandooriflames.ca/', 'http://www.hoodlumproducts.com', None, 'http://Www.Lolasallys.ca', 'http://www.synergytanningnorthyork.com', 'http://antoshabakery.com/', None, 'https://www.vegastvmounting.com', 'http://mrcm.ca', 'http://www.cityofelmirage.org/index.aspx?NID=1415', 'http://www.tarheel4wdcenter.com', 'http://deerfootinn.com/casino/mojave-grill', 'http://www.clevelandbartendingschool.com', 'https://www.hilton.com/en/hotels/cleeyhx-hampton-suites-elyria/?SEO_id=YELP-HP-CLEEYHX', 'http://www.ilovechurros.com', None, 'http://www.wolfevalleyelectric.com/', None, 'http://armoryprintworks.com', 'http://yum-bakery.com/', 'http://www.dynamixxentertainment.com/', None, None, 'http://www.brindleysmusic.com/', None, 'https://www.wyndhamhotels.com/hotel/14897?tel=18002521709&iata=00065402&cid=fe:ra:20161215:yl:pp:ramus:14897', None, None, 'http://www.citylifeusa.com', 'http://www.sunridgegolf.com', 'http://www.littlepeeps.ca/', None, 'http://www.phoenix10k.com', 'http://releviumpain.com', 'http://www.corbinsbarandgrill.com', 'http://www.jwebb.net', 'http://columbusbros.com/index.html', None, None, 'http://www.vulcanvet.com/', 'https://us.megabus.com/?utm_source=Yelp&utm_medium=Yelp&utm_campaign=Charlotte%20Page', 'https://www.schillerhamilton.com', 'http://www.applebeescanada.com/restaurants/information/calgary-sunridge', 'http://www.advanceddentalnv.com/', None, 'http://www.shalimarbistro.ca', 'http://www.clemetparks.com/visit/index.asp?action=rdetails&reservations_id=1014', 'http://www.sienapediatrics.com', 'http://www.walgreens.com/locator/walgreens-15490+w+bell+rd-surprise-az-85374/id=4620', 'http://www.bistroontheavenue.com/', None, None, None, 'http://www.aa.com/admiralsclub', 'http://visionaryacupuncture.com', 'https://www.avondalegatewaydental.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://www.gandermountain.com/store-locator/details/Gastonia-NC-333', None, None, 'http://saltedmalted.com', 'http://www.sears.com/stores/new-jersey/woodbridge/0001684.html', None, 'http://www.bk.com', None, 'https://primethreading.com', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.quailvalleyoncarmel.com/', None, '1592339929', 'http://fastandfriendlycarwash.com/locations/peoria', 'http://www.horseshoetavern.com', None, None, 'http://www.starwomancrystals.com/', None, None, None, 'https://www.cafemayakovsky.com', 'http://www.crudoaz.com', 'http://www.pro-tectsecurity.com', 'https://www.evolutioncustoms.com', None, 'http://www.ultimateconcretelv.com', 'http://thepizzapop.ca/index.html', 'http://www.cafemoi.ca', None, 'http://planetbeach-expressaz.com', 'https://fifth-group.com/pan-asian-express', 'http://vitalityint.com/contact-us', 'http://restaurantdepot.com', 'http://aaautomotiverepairs.com', 'http://www.gottalovecheesecake.com', 'http://www.flashmoversnow.com', 'https://corsoshoes.com', None, None, 'http://www.ajsmusic.com', 'http://avondaledodge.com', 'http://www.mbrgr.com/english.html', None, 'http://bronzedtan.com', 'http://www.boilerhouse.ca/', 'http://www.thomasmertoncenter.org/thrifty/', 'http://www.workshopgallery.ca', None, '1592340015', 'http://torontojdm.com/', 'http://www.einsteinbros.com', 'https://www.fastmed.com/urgent-care-centers/phoenix-az-walk-in-clinic-maryvale-parkway/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.burgerfactory.ca', 'http://www.dflaz.com', None, 'http://www.woodreface.com', 'http://gabbys.ca', 'https://locations.theupsstore.com/oh/medina/3593-medina-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://blvdpubandkitchen.com', 'http://www.felicitybeauty.com', None, None, 'http://www.tanekotavern.com', None, None, 'https://www.mcdonalds.com/us/en-us/big-mac-trio.html?cid=PS:GCM_MOP:NB::Yelp:All', 'http://harvestnoon.com/', 'http://www.goodlifefitness.com', None, 'http://www.royalpaan.com/store-brampton-south-hurontario.html', 'http://www.qualitydentalsmile.net', None, 'http://www.kettlemuckstoyshoppe.com', 'http://www.rickspoolcare.com', 'http://www.elysianatthedistrict.com', 'http://www.americaneyeglassrepair.com/', 'http://www.timhortons.com', None, 'http://www.bonappetitdescaraibes.com/', None, 'http://www.jewelryarthudson.com', None, 'http://www.crossfit623.com', None, 'http://www.lukewholey.com', '1592340101', 'http://www.szmidts.com', 'http://office71634.wix.com/riverview-pcusa', 'http://Www.pacificjunctionhotel.com', 'http://www.bankofamerica.com', 'http://www.personaltouchcleans.com', 'http://www.chutneysmadison.com', 'http://marquessjewellers.com/', 'http://www.americanbikeandtrike.com', 'https://www.walmart.com/store/2554/avondale-az/details', None, 'https://www.thebodyshop.com/en-us/?utm_source=yelp&utm_medium=yelp&utm_campaign=us_180418_w19_search_bau&utm_content=websiteurl', 'http://www.jtwhitneys.com', 'http://garrisonbespoke.com', 'http://craftkitchen.ca', 'http://www.regalnails.com', 'http://www.MikadoAZ.com', 'http://www.bakerblvd.com/', None, 'https://www.ellsworthhomeservices.com', 'http://www.firstdancecharlotte.com', 'http://www.affordablemufflerinc.com/', None, 'http://www.catosautosalon.com', None, None, None, None, 'http://www.portrestaurant.ca', '1592340164', 'https://www.phoenixconventioncenter.com', 'https://www.castorage.com/storage/nevada/storage-units-las-vegas/3350-Sirius-Ave-239', None, 'http://az-contracting.com', 'http://elevenlakesbrewing.com', 'https://www.applebees.com/en/restaurants-murrysville-pa/4920-william-penn-highway-78035', 'http://www.seriouslyskin.com/', 'http://www.laurakuhl.com', 'https://www.avis.com/en/locations/ca/on/toronto/b02', 'http://www.eathopscotch.com', '1592340193', 'http://www.parmabychefmarc.com/', 'http://www.woodland-studios.com', None, '1592340202', '1592340205', None, 'http://dragongardenrestaurant.food-places.com', None, 'http://www.wolfsonmedicalcenter.com', 'http://www.demetriosbride.com/', 'https://drivewoodfiredgrill.com/about-us', None, '1592340225', None, 'http://www.goodwillsp.org/shop/retail-stores/pineville/', 'https://offbeatandunique.com', 'http://www.serviceking.com/locations/service-king-champaign?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://www.kennywood.com', None, 'http://www.hallfamilydentistry.com', None, None, '1592340247', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'http://vickigreco.com/', 'https://www.cherrylash.com', 'http://pronailspamadison.com', 'http://www.petro-canada.ca/', 'http://www.arbys.com/', 'http://www.eagleviewrvresort.com', 'http://www.blackmountaintowing.com', None, 'http://www.mybobs.com', '1592340268', 'http://www.fullertonfp.com', 'http://affordablewindowtintinglv.com', 'http://ad.doubleclick.net/ddm/clk/284948194;111994992;d?http://delanolasvegas.com/spa/bath-house-spa.aspx', None, 'https://babel-mediterranean-market.business.site', 'https://www.ihop.com/en/restaurants-phoenix-az/5020-e-ray-rd-1508', None, None, 'http://www.hakkacanadiancafe.ca', 'http://www.lavamassageandskincare.com', None, 'http://www.dollartree.com/home.jsp', None, 'http://www.karenbiscotti.com', 'http://arizonaurologyspecialists.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', 'http://larasrestaurant.com', '1592340309', None, 'https://union.wisc.edu/dine/find-food-and-drink/peets-coffee-and-tea/', 'http://www.ripplingerfamilydentistry.com', None, 'https://www.mattressfirm.com/stores/nc/concord/mattress-stores-concord-nc-28027-6186.html', None, 'https://www.petsmart.com/stores/us/az/scottsdale-store0130.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://www.aaautocarelv.com/locations/400-simmons-st/', None, None, 'https://dorhoutchiropractic.com', None, 'http://www.tsdental.ca', 'http://www.WestbrookAH.com', 'https://www.myeyedr.com/locations/mint-hill?utm_campaign=mint-hill&utm_medium=Referral&utm_source=Yelp', 'http://azhealthquest.com/', 'http://www.slymanstavern.com', None, None, None, 'http://www.houseatsecretgarden.com', None, 'http://www.braggsdiner.com', None, 'https://www.searsauto.com/stores/6661?psid=campaigncode-6661', None, 'http://www.crazylennysebikes.com/', 'http://jonesmoverz.com', 'http://www.dairyqueen.com', None, 'http://www.akanesushi.com', None, 'http://www.spraggsmeatshop.com/', '1592340385', 'http://www.cartelcoffeelab.com', None, 'https://www.gopanache.com/pro/mroffthetop', None, 'http://bottle-service-las-vegas.com', 'http://www.rossstores.com', 'http://matthewsbarbershop2.com', None, 'http://www.puredelitecupcakes.com', 'http://donnellygroup.ca/belfast-love/splash', None, 'http://www.greenhousejuice.com', 'http://www.kmart.com/stores/ohio/garfield-heights/3278.html', 'http://www.firehousesubs.com/?ref=yelp', 'http://www.dignifiedhomeloans.com', 'http://www.bayblooroptometry.com', 'http://www.thetemperedroom.com', None, 'http://vintageautorepair.net', '1592340432', 'http://www.miracleshieldcarcare.com/', 'http://www.hongkongfoodmarket.ca', 'https://stores.mooresclothing.com/on/newmarket/17820-yonge-street.html?utm_source=yelp&utm_medium=listing&utm_content=25&utm_campaign=ON', None, None, None, None, 'http://www.pizzeriafabio.ca', 'http://stores.thenorthface.com/ON/TORONTO/TNF-151BSWTO-1/', None, 'http://www.poolbarrieraz.com', None, 'http://barmontauk.com/', 'http://www.squishcandies.com/en_ca', None, None, None, 'http://www.draugustine.com', None, None, None, None, 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', '1592340486', 'http://www.tmapplianceservice.ca', 'http://www.childtime.com/your-local-school/indian-trail-nc-2014/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, 'http://www.tsa.gov/tsa-precheck/', None, '1592340497', 'https://oprdisabilitylaw.com', 'http://BurgherBurger.com', 'http://www.GriffinHomeHealthCare.com', 'http://www.ycstrans.com', '1592340510', None, '1592340515', None, None, 'http://dhcustomz808.com', None, 'http://artforumframing.com', None, None, None, 'https://info.donvalleynorthcollision.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.lubestop.com/Locations/Cleveland-Heights', 'http://www.jtalleymd.com', None, None, 'https://www.cirquedusoleil.com/usa/las-vegas/deals?ci', 'http://woodys-barbq-calgary.business.site', 'http://acesgrille.com', None, 'http://www.DLCphoenix.com', None, 'http://silveradobathandremodel.com', 'http://TheMoralesTeam.com', 'https://www.thetenspot.com/ajax/', 'https://www.acelawgroup.com', 'http://www.universalglassaz.com', 'https://www.sierragrandeapartments.com', None, None, 'http://www.verizonwireless.com/b2c/index.html', 'http://us.suitsupply.com/en_US/store?StoreID=stores-LasVegas&utm_medium=referral&utm_source=yelp&utm_campaign=Las_Vegas', None, 'http://www.galleriaatsunset.com', 'http://ad.doubleclick.net/clk;280858415;107462676;p', 'http://www.nhprimarycarefoxcroft.org/', None, None, 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', None, None, 'http://www.tattoodamerica.com', 'http://www.littlecaesars.com/', 'http://www.lucky13tattoos.ca', 'https://locations.theupsstore.com/az/scottsdale/16211-n-scottsdale-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.bergerallied.com/las-vegas-movers/', '1592340615', None, 'http://www.banfield.com?utm_source=yelp&utm_medium=PAID&utm_content=yelp_general&utm_campaign=YelpPaid', 'http://www.redhawkrentals.info', 'http://www.thebeautyhouse.ca', 'https://www.goldenhorserestaurant.net', None, None, None, 'http://www.dollar.com/Locations/gen.aspx?locationId=PIT', 'http://www.pkwytavern.com', 'http://www.brothersthreemadison.com', '1592340646', 'http://topnailslasvegas.com', '1592340651', 'http://www.thelaserlounge.ca', None, None, None, 'http://NewmarketInfiniti.ca', 'http://www.rockinghranch.com', 'https://www.matthewjeffery.com', 'http://www.sloanboutique.com', 'http://www.lasvegasleansixsigma.com', 'http://TheBodhi.com', 'http://www.lefagotin.ca', None, None, 'http://www.calgarymoverspro.ca', None, 'http://ljhaircuts.com/index.html', 'http://www.sears.com', 'http://www.antronightclub.com', 'http://inspirelasvegas.com/wayfarer-theater/justin-tranz/', '1592340697', 'http://www.ajisai.ca', 'http://www.the-grove.com', 'https://samsxpresscarwash.com/indian-trail/', 'http://www.sushikeemesa.com/', 'http://www.readingsbygenevieve.com', 'http://www.acehardware.com/store-details/14577', 'http://www.toplinetailoring.com/', None, 'http://firstchoice.com/salondetail/default.asp?salonid=5068', 'http://www.allstarwingsandribs.com', 'http://www.dignityplumbing.com', 'https://bostonpizza.com/en/locations/sunridge.html', 'http://www.kevinscomputer.com/', None, None, 'http://www.aznaturalmedicine.com', 'http://locations.fazolis.com/search.html?q=61821', None, 'http://www.sportchalet.com', 'http://www.kvegas.com', 'http://www.7-eleven.com/?yelp=29384', None, 'http://www.timhortons.com/', 'http://freezersicehouse.com', 'http://www.discount-drugmart.com', 'http://www.eatjackpot.com', 'http://www.tegacayanimalhospital.com', None, 'http://hairuntangled.com', 'http://www.creativehandscuisine.com', 'http://www.swisschalet.com', None, None, '1592340780', None, 'https://www.aaautocarelv.com/locations/aa-auto-care-sunset-rd/', None, 'http://www.chuggersbar-grille.com', None, None, 'http://www.skyforall.com', 'http://www.theazcs.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YULMA', None, None, 'http://www.livbaylash.com', 'http://www.famouslaffa.com', 'http://www.mckellipsinternalmedicine.com', 'http://www.findlayhondahenderson.com', 'https://www.dearfro.ca', 'http://discountopticaltoronto.com', 'http://www.infinityinsurancepartners.com', 'https://www.intownsuites.com/extended-stay-locations/north-carolina/kannapolis/kannapolis/', 'http://www.aloha-ac.com', None, None, None, 'http://www.soldiersandsailorshall.org', None, 'http://www.djtoyota.com', None, 'http://www.ippeijapanesebistro.com/', None, 'http://azrentalhomes.com/property-management.php', None, None, 'http://shopvoc.com', None, 'http://spapoolbilliards.com', 'https://mobileskinscreening.com', 'https://www.wellsfargo.com', None, 'http://www.touringcarinc.com', 'http://www.dsw.com', 'http://www.shaingallery.com', None, None, None, 'http://www.brosdough.com', 'http://www.cafe16yyc.com', 'http://www.thriftycarsales.com/Thrifty_Gilbert/Home', 'http://www.702sunrisedental.com', 'http://www.freshandeasy.com/', '1592340901', 'http://www.starbucks.com/store/15887/', 'http://championchandler.org/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/LASBR', 'http://www.confectionique.com', 'http://www.americanfence.com', 'https://www.wiglewhiskey.com/whiskey-garden', 'http://www.signaturestylehairstudio.com', 'http://www.rebuildtrans.com', 'http://www.shipriteoffice.com', 'http://www.liquorstorevegas.com', 'http://www.goallininc.com', None, None, 'https://www.drkellydds.com', 'http://mononabaiticecream.yolasite.com', 'http://www.auto-links.ca', None, None, None, None, 'http://www.drugandalcohol24-7.com', 'http://www.globecinema.ca', 'https://www.camdenliving.com/charlotte-nc-apartments/camden-cotton-mills', None, 'http://www.atlaschiropracticphoenix.com/', None, None, None, 'http://partywithpaint.com', 'http://blvdpubandkitchen.com', 'http://www.leashandpaws.com', None, 'http://www.secondcup.com/location/toronto-355-danforth-avenue', 'https://maps.rbcroyalbank.com/locator/searchResults.php?t=6702', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.tangerineom.com', 'http://www.greenbushbakery.com', 'http://www.lowes.com', None, 'http://www.teresaspizza.com', 'http://www.primrosefletcherheights.com/?utm_source=yelp&utm_medium=maplistings&utm_campaign=localmaps', 'https://www.katsurdentalaz.com/offices/peoria/', 'http://www.the-alley.ca', 'http://copperstatefloors.com', 'http://www.shawarmabarvegas.com', 'http://www.elliotdentalcorp.com', None, 'http://www.teambuildingandtraining.com/team-building-las-vegas/', None, None, 'http://www.courtesylotus.com', 'http://www.falloutgames.net/home.html', 'http://www.bostonpizzavegas.com', 'http://www.toronto.ca/parks/prd/facilities/complex/543/index.htm', None, 'http://www.napaautorepairaz.com', 'https://www.palmvalleydentallasvegas.com', 'http://windsor-jewelers.com', 'http://trutea.ca', 'http://hugoscellarlasvegas.24cafes.com', None, 'https://www.bwalk.com/en-CA/Rent/Details/Alberta/Calgary/Northwest-Pointe?utm_source=Yelp+Website', 'http://www.phoenixvalleylandscaping.com', None, 'http://www.90degreessalon.com', 'https://www.cpapclinic.ca', 'http://www.labelsexchange.ca', 'http://www.fountaincuisine.com', 'http://www.poolandlandscapeaz.com', None, 'http://www.eljacalaz.com', None, 'http://www.tacticalpestcontrolllc.com/', 'http://www.ginzavaughan.com', None, None, 'http://www.bajafresh.com/mexican-food-texas-station/', 'http://www.7-eleven.com/?yelp=22886', None, None, 'https://www.dominos.com', 'http://carcleanersdetailing.com', None, None, 'http://www.eggsmart.ca', 'https://www.wingstop.com/location/wingstop-678-laveen-az-85339/menu', 'http://www.thebay.com/webapp/wcs/stores/servlet/en/thebay#!/', None, 'http://www.targetknives.com/', 'http://www.patisseriemanon.com', 'http://www.pitakababgrill.com', 'http://www.britewintercleveland.com/', 'http://www.urbanaboulders.com', None, None, 'http://www.tiffanysbakeryohio.com/', 'http://bouffantsalon.webs.com', 'http://www.shopalix.com', 'https://www.hairclub.com/locations/az/phoenix/hair-loss-clinic-281/?pub=loclisting&utm_source=yext&utm_medium=loclisting&utm_campaign=YX_281', None, 'http://www.montgomerysrestaurant.com', None, 'http://www.stevescycle.us', 'http://www.forever21.com', 'http://www.lakeviewmesa-apts.com/switch_cls%5Bid%5D/34626', 'http://www.slixer.com/', 'http://drjameshong.com', 'http://www.tasteofmediterranean.ca/', 'http://arizonaurologyspecialists.com/darson', 'http://helmuthgaragedoorco.com', None, 'https://www.balsamdayspa.com', 'http://www.mybeautyrecess.com', 'http://www.impgilbert.net', None, None, 'http://www.nightanddaydecor.com', 'http://gettingerchiropractic.com', None, 'http://b-g-tree-service.business.site', None, 'http://www.toryburch.com/store-details?StoreID=tro_ca_toronto', None, 'https://leperformance.com', None, 'https://stahlplumbinganddrain.com', None, None, 'https://www.PeccoleRanch.net', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sequel.ca/', 'http://www.1stclassautotransport.com', None, 'http://www.buttercupbabylv.com', 'http://www.neighborhoodvisioncenter.com', 'http://stores.sportsauthority.com/az/phoenix/sporting-goods-phoenix-700.html', 'http://www.cafebabareeba.com/', None, 'http://newhorizonnailsandspa.com', None, 'https://www.knightsinn.com/North-Black-Canyon-Hwy-Phoenix-AZ', 'https://opasouvlaki.ca', None, None, None, '1592341243', 'http://www.barhopbar.com/', 'http://www.hiriseliving.com/las-vegas/high-rise-condos/turnberry-towers', '1592341252', 'http://marklandwoodpharmacy.ca/', None, None, None, 'https://www.bannerhealth.com/locations/gilbert/banner-urgent-care-2', None, 'http://www.heroburgers.com', 'http://Www.daango.com', None, None, 'http://www.starbucks.com/store/9334/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://haircutmenmtlebanonpa.com', 'http://www.tjmaxx.com', '1592341288', 'http://www.protectamerica.com/shop/order-package?agent=A11117', 'http://www.abcscapes.com', None, None, 'http://thebluescan.com/', 'http://Www.shogunwhitby.com', 'http://www.airgas.com', 'http://www.luxyclub.ca', 'http://www.wirelesstoyz.com', 'http://www.dunkindonuts.com', 'https://www.presscoffee.com', 'http://www.bigotires.com/regions/Nevada', 'https://www.bankofamerica.com', '1592341325', None, 'http://www.djsdaycare.com', 'http://www.cleanchoice.com/', None, 'http://walkwithmeg.com/', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.haguepartners.com/', None, 'http://www.wildfirecrossfit.com', None, 'http://TheGrayson-Apts.com', 'https://www.orangetheory.com/en-us/locations/south-carolina/fort-mill/1329-broadcloth-street-rnsuite-105/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://tuftandneedle.com', 'http://thecarpetmedicnc.com/', None, '1592341364', None, 'http://oneworldshopcle.com', None, 'http://www.HonestAirCare.com', 'http://www.cmlibrary.org/locations/branches.asp?id=18', 'http://hollyeyewear.com', 'https://www.phoenixflowershops.com', 'http://www.myshapelipo.com', 'http://fourdogspetsupplies.com', 'http://gskinbeautyinstitute.edu/las-vegas-beauty-school/', 'http://glossnailbarlakewylie.com', None, 'http://www.breadsmith.com/fort-mill/', 'http://pulpjuiceandsmoothie.com', 'http://www.urbanluxerealestateaz.com', 'http://www.driftsalon.com', None, 'https://www.merryhillschool.com/preschools/las-vegas/durango-dr/?utm_medium=directory&utm_source=yelp&utm_campaign=paid_listing&utm_content=website', 'http://www.vivethabistro.com', None, 'http://www.cousinsmarket.com', 'http://www.tattlifestudios.com', 'http://www.craftyburgr.com', 'http://www.figaros.com/', 'http://www.alibabas.ca/index.php?route=common%2Flocation_details&loc_id=1', None, None, None, 'https://omalzafitness.com', None, None, 'http://www.americasmattress.com/charlotte', 'http://synergyvapor.com', 'http://www.gilbertfamilydentist.com/', 'http://www.bobbyshideaway.com/', 'http://www.eyelidsurgeries.com', 'https://www.wellsfargo.com', None, 'http://www.bk.com', 'http://dspotdessert.com', 'http://www.uptownbrides.com/', None, 'http://www.hoghauling.com/', None, 'http://www.lasvegaspartysupply.com', 'http://www.pacini.ca', None, None, None, 'https://www.walmart.com/store/1380/las-vegas-nm/details', None, 'http://www.villageofstreetsville.com/', 'http://www.blackmarketminerals.com/', None, 'http://www.acaciacocktails.com', 'http://backstage-hair.com/index.html', None, 'http://www.fantasticsams.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.mrosmow.com', 'http://www.izod.com', None, None, None, 'https://www.caesars.com/ballys-las-vegas/things-to-do/pool?utm_campaign=Yelp&utm_term=BluPool&utm_medium=local&utm_source=yelp&utm_content=pool', None, 'http://familycomforthospice.com', 'http://www.westonfavourites.com', 'http://www.lvreal.com', 'http://www.hrh.ca/', 'http://www.fushimi.ca/', None, 'http://blackhawkhardware.com', None, 'http://www.Lovxurioushairloft.com', 'http://www.fullerspatiomistingsystems.com/', None, 'https://www.annassewingcenter.com', 'http://www.canyoncrossroads.com', 'http://luluhawaiianbbq2lasvegas.goodbistros.com', 'http://www.scottsdaleweightloss.com', None, 'http://www.rush2tan.com', 'http://professionalshoerepair.ca', None, 'https://www.joshuahillslasvegas.com', 'https://www.goodfellasgrillphoenix.com', 'https://www.worcesters.com', 'http://www.matthewsfunmachines.com', 'http://lilcritterspest.ucoz.com', 'https://www.costco.ca/warehouse-locations/s-mississauga-mississauga-on-531.html', 'https://www.1800packrat.com', 'http://www.phantomoftheattic.com/', None, 'http://bradshawsocialhouse.com/', 'http://southsidecarpetcleaning.net', '1592341594', 'http://www.flysunwing.com', 'http://www.azwholesalebikes.com', 'http://inkoninkoff.com', 'http://www.salon1219.com', '1592341610', None, '1592341615', 'https://www.honorhealth.com/locations/specialty-care/honorhealth-heart-institute-north-mountain?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-heart-institute-north-mountain', 'https://www.smalv.com/OurCenters/ConvenientCares', 'http://www.littlecaesars.com/', 'http://www.dutchfixmycar.net', 'http://www.sandersonford.com', 'http://www.bahamabucks.com/', 'http://saharagoldandsilverbuyers.com', '1592341635', 'http://drtomkoustis.com', 'http://www.acomaanimalclinic.com', 'http://www.24sevenpro.com', None, None, 'https://www.floattheriver.net', 'https://apusnailspascottsdale.com', 'http://www.graveslabradors.com', 'https://willowdalemedicalclinic.ca', None, None, 'http://www.cleanyourdirtyface.com', 'http://greenmoversofamerica.com', None, 'https://thesoutherngourmet.net', None, None, 'https://local.fedex.com/oh/richmond-heights/office-1915/', 'https://www.t-mobile.com/store-locator/oh/parma/snow-rd-broadview-rd?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.lush.com', 'https://www.dcranchmd.com', 'http://www.target.ca', 'http://www.amysdoughnutfactory.com', 'http://www.dolcini.ca/', None, 'http://www.jackmcvicker.com', 'http://www.leviettoronto.com', '1592341699', None, None, 'http://www.anglesroyaloak.ca', 'http://www.littlecaesars.com', 'http://www.exclusiveautomotiverepair.com', None, 'http://www.subbro.com', None, 'http://www.olphaz.com', None, None, 'http://spa810.com', 'http://www.myamybridal.com', 'http://www.stratospherehotel.com/Food-Drink/CBar', 'http://www.aaacarolinas.com', 'http://rejenesysmedspa.com', None, 'http://www.courtyardchiro.com', 'http://www.nailsbyreesunshine.com', 'http://www.crownlithoequipment.com', None, None, 'http://www.woodrepaircharlotte.com', None, 'https://www.cineplex.com', None, 'http://www.sprint.com', None, 'http://salsaritas.com', None, 'https://stores.jcpenney.com/az/phoenix/clothing-stores-phoenix-az-2846.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2846', 'http://www.philippelusi.com/', None, 'http://www.kwikpicklockandsafe.com', 'http://www.carminesgroup.com', None, None, 'http://www.bicyclesatstclair.com', None, 'http://bodyspasalons.com/best-salon-and-spa/green-valley-salon-and-spa-henderson/', 'http://taylorandcolt.com/royal-bank-plaza-toronto/', 'http://www.bobscopyshop1.com', 'http://www.mecklenburgbridal.com', 'http://www.bfmrestaurant.com', 'http://www.leesakasslerdesigns.com', None, 'http://www.thequeenoftarts.ca', None, 'https://www.kohls.com/stores/wi/madison-213.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.personalinjurylawyertorontodirect.com', None, 'http://royalimpactcda.com', 'https://www.covecommunities.com/calgary', 'http://www.springhillbrewing.com', 'http://www.mrosmow.com', 'http://coldpressexpress.com', 'http://www.jerseysolarlasvegas.com/', 'http://www.alterationsidea.com', 'http://cosmedixmd.com/', None, 'http://www.mypubliclibrary.com', 'http://fuzzwaxbar.com', None, 'http://www.arbys.com', 'http://agreatsmileaz.com/', 'https://www.trulynolen.com/location/arizona/chandler-pest-control?utm_source=yelp&utm_medium=listing&utm_campaign=', 'https://www.remedystaffing.com/locations/madison-east-wi/67962-6041', 'http://www.rocndocs.com', 'http://lasvegasmobilegroomer.com/Home_files/Page355.html', None, None, None, 'https://cobblestone.com/?utm_source=yelp%C3%8A', 'http://www.freedommilitarysurplus.com', None, None, 'http://www.totalwine.com/store-info/nevada-las-vegas-summerlin/1201', None, 'http://www.KwanNaturopathic.com', 'https://bestbuytirecleveland.com', 'http://www.willownaturalfoods.ca', 'https://www.morgancommunities.com/apartments/pa/pittsburgh/morgan-at-north-shore/', 'http://www.skettleelectric.com', None, 'http://www.bhttransportationinc.com/', 'http://www.arianamotorslv.com', None, 'http://www.localeatspizza.com', None, 'http://www.gordysbootcamptoronto.com/', 'http://noodlepotlasvegas.gastro-america.com', None, None, 'http://livenexa.com', 'https://www.nplusonecafe.com', 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', 'http://www.sleeprover.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://lasvegasliving.com/properties/san-croix/', None, 'http://www.azangelsgreen.com', 'http://www.arrowheadcarpettile.com', None, 'http://www.williamsmoving.com', 'http://www.jonesmotors.com/', 'https://www.tavernettayyc.ca', 'http://www.gloriasblossoms.com', 'http://www.terribleherbst.com', None, None, None, None, 'http://www.heathloans.com', None, None, 'http://medicalspagilbert.com', 'http://www.azfoothealth.com', 'http://www.adt.com', 'http://www.gianteagle.com', None, 'https://www.9roundkickboxinggilbert.com', None, None, None, 'http://thefashioncleanersaz.com', 'http://www.lazeezgrill.org', 'http://www.redstonegrillelv.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://lauravegashomes.com', 'http://www.elitelaser.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://scottsdale.certapro.com//?source=Yelp', 'https://www.petsmart.ca/stores/ca/on/newmarket-store1126.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', 'http://www.bk.com', 'http://stylettoz.com', None, 'http://h2photo.ca', 'https://www.summerkidsdental.com', None, None, None, 'http://www.suncityexpress.com', 'http://myamtrans.com', 'https://agents.farmers.com/az/tempe/ashlee-candelaria?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', None, 'http://www.starbucks.com/store/9298/', 'http://blushsalonarizona.com', '1592342086', 'https://www.solitairejewellery.com', None, 'http://www.Brushfiretacos.com', None, 'http://drshawnsullivan.com', None, 'https://www.legacyroofingllc.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.fourpointstorontolakeshore.com?EM=YELP_4P_1243_NAD', 'http://www.rambleandrescue.com', None, None, 'http://www.tomdevlinsmonstermuseum.com', None, 'https://www.ontario.ca/page/serviceontario', 'https://wildfire.sclv.com/WildGrill?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'https://redrock.sclv.com/Entertainment/Lounges-and-Bars?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', 'http://www.kismetmadison.com', 'https://barkavepet.com', 'http://garb.ca', 'https://www.iip-management.com', 'https://www.imtresidential.com/superstitionvista/?utm_source=yelp&utm_medium=ilslink', None, 'http://www.wholefoodsmarket.com/stores/LVB', 'https://www.wedgewoodweddings.com/venues/nevada/stallion-mountain?utm_source=yelp&utm_medium=social&utm_campaign=stallion-mountain-yelp', None, 'http://www.desertmemorial.com', None, 'http://juicdlife.com', 'https://www.sethsellsinsurance.com?cmpid=nseg_blm_0006', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', None, 'http://smogbusters.com', 'http://www.capstonedentalnc.com', 'http://www.ubreakifix.com/locations/pittsburgh', 'http://newimagewindowtintandautoglass.com', 'http://mountainparkhealth.org', '1592342181', 'https://www.walmart.com/store/2592/north-las-vegas-nv/whats-new', 'https://www.rei.com/stores/pineville.html', 'http://www.silverspoononline.com', 'http://davidsonspub.com/', 'https://www.integratedio.com', 'http://www.interchangefinancial.com/contact/toronto-downtown/', 'http://www.starbucks.com/store/17296/', None, None, 'http://kidtokid.com/peoria', 'https://www.fit4less.ca/locations/provinces/ontario/etobicoke/etobicoke-kipling-queensway', 'http://www.freedomfitnesstroon.com', 'http://www.eliteeyelv.com/', None, 'http://www.ztrip.com', 'http://www.bentleyflooringaz.com', 'http://www.drtaylordentistry.com', 'https://www.lifetimefitness.com/spa/spa-salon.html?utm_source=yelp&utm_medium=directory&utm_campaign=SCT-acquisition', 'http://www.cosmoholicsalonllc.com', None, 'https://goshango.com/locations/nevada-dispensaries/shango-las-vegas/', None, None, 'http://www.tcby.com/', None, 'https://federicosmexicanfood.com', 'http://sandysdeliandcatering.com/index.htm', 'http://www.dunkindonuts.com', 'https://smashburger.com/?utm_source=yelp&utm_medium=organic', 'http://www.chocolateshoppeicecream.com/node/3245', '1592342262', None, None, '1592342270', 'http://www.orthopedicsportstherapy.com', None, 'http://www.RandomAlchemy.com', 'http://www.balloonplanet.com', None, None, 'http://www.madisonavenuepub.com/madisonmanor', 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store186', 'http://locations.atipt.com/phoenix-az', 'http://www.iloveburgers.com', 'http://www.davidsonbelluso.com', 'http://pittsburgh.blasterbouncer.com', None, 'http://luxurynailsbarpeor.wix.com/nails', 'http://www.simonsbrecksville.com/', 'http://carolinabeertemple.com/', 'http://local.firestonecompleteautocare.com/nevada/nellis-afb/5790-rickenbacker-rd-bldg-606/?lw_cmp=IYP_YPC_MLP_344698', None, None, None, 'http://www.lightingaz.com', 'http://www.fillaseatoc.com', None, 'http://www.marriott.com/hotels/travel/cltru-residence-inn-charlotte-uptown/', '1592342330', 'http://serenitysalonsuites.net/salons/bbs', 'http://www.animalemergencydurham.com', 'https://www.icon2900.com', '1592342341', 'http://www.estheticfinesse.com', 'http://www.sagra.ca', 'http://www.kimvo.com', 'http://www.desertgatorpools.com', 'http://www.sweetthangcupcakes.com', 'http://www.orojewelers.com', 'http://Vintagejoes.com', '1592342361', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', '1592342366', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.usps.com/', 'https://www.thejoint.com/arizona/avondale/gateway-crossing-48019', 'http://www.freshburger.ca', 'https://www.moosepest.fullslate.com', 'http://www.acecustomtattoo.com/home.htm', 'https://www.applebees.com/en/restaurants-strongsville-oh/17771-southpark-center-91085', 'https://www.wyndhamhotels.com/hotel/51450?tel=18885953511&iata=00093785&cid=fe:wg:20170523:yl:pp:winus:51450', 'http://www.thebiggreenk.com/locations/mint-hill.aspx', None, None, 'https://locations.theupsstore.com/nc/matthews/2217-matthews-township-pkwy?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.palms.com/the-view.html?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://myrockstarparty.net/', None, None, 'http://www.xtreme-play.com', 'https://www.familytrust.org/', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.azbreadco.com', 'http://www.danforthlumberhbc.com', 'http://www.spgrocery.com/', 'http://www.vagabondo.ca', 'https://www.fastmed.com/urgent-care-centers/glendale-az-walk-in-clinic-happy-valley-road/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.tommytuckers.com', 'https://www.samsclub.com/club/las-vegas-nv-sams-club/8177', 'http://creativeinteriorsolutions.us/', None, 'http://newdaycafelv.com', 'http://flowerfields.ml', 'http://www.theboatkensington.com/', None, None, 'http://theblendaz.com', 'http://www.gnc.com', 'http://www.containerstore.com', 'http://www.dutchauto.wordpress.com', None, 'http://www.allpet.org', None, None, 'http://www.dominos.com', 'http://www.starbucks.com/store/14290/', '1592342472', None, None, 'http://www.verotrattoria.com/', None, 'http://golfpleasantvalley.net', None, 'http://www.johnnyjackson.ca', 'http://www.scottsdalepartybuslimo.com', 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, None, 'http://www.einsteinbros.com/', None, None, 'http://www.saksfifthavenue.com/Entry.jsp', None, 'http://www.plazakia.com', 'http://www.imperialpool.com', None, 'http://www.indianmotorcyclechandler.com/', None, 'http://www.terragreenlandscape.com', None, 'http://barlowautopro.com/', 'https://www.bankofamerica.com', None, None, 'https://www.landroverchandler.com', 'http://www.alloptionsfuneralhome.com', 'http://www.fiftysixwest.com', None, 'http://www.monkeywrenchaz.com', None, 'http://www.mahlaantiques.com/', None, 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=442', 'http://www.nevadayachtclub.org', None, 'http://www.partsauthority.com', 'http://www.souvlakiexpress.com/', None, None, None, 'https://www.pvwomenscare.org', 'http://thevenetian.ca/', None, None, 'http://www.hdcleaningpgh.com', 'http://www.popcorngirlvegas.com', 'https://www.spencerstv.com/locations/scottsdale_phoenix.html?utm_source=website%2013820', 'http://www.holeechow.com', 'https://www.tommykplay.com', None, 'https://bostonpizza.com/fr/locations/vaudreuil.html', None, None, 'https://www.panerabread.com/en-us/home.html', 'http://zilchflorist.com', None, 'https://luna-boutique.co', 'https://www.mrshinecarwash.ca', 'http://Juansflamingfajitasandcantina.com', 'http://www.goodwillaz.org/', 'http://www.albaikpizza.com', None, 'http://www.redendos.com', None, 'http://calgarytavern.com', 'http://www.cccnevada.com/doctor/john-jack-collier-md-fccp-dabs/', 'https://www.aqua-tots.com/matthews/', 'https://www.bathandbodyworks.com?cm_mmc=local_BBW02046', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, None, 'http://www.uadc.org', None, 'http://www.celebritytanning.com', None, 'http://www.meineke.com', '1592342662', None, 'http://www.papajohns.com', 'http://Www.cleaningdepotstore.com', 'https://www.itcu.org/about/locations/green-valley', 'http://www.teavana.com', 'http://www.actinoliterestaurant.com/', 'http://www.championremodelingaz.com', 'http://www.goodearthcafes.com', 'http://www.apachetattooaz.com', None, 'http://www.sutrasushi.com', None, 'http://rosiesto.com', None, 'https://www.silvercar.com/#/locations/17', 'https://www.americanwarriorautoglass.com', 'https://3bowls.com', 'http://larsana.com', None, None, 'http://oasisvape.com', None, 'http://www.residentialgourmet.com', 'http://www.Source1Phones.com', None, None, 'http://www.mycarhurts.com', 'http://www.anandorestaurant.ca', 'http://www.Josephscoatpainting.com', 'http://www.thetuscaninnzc.com/', 'http://www.pinkshotdogslv.com', 'http://www.maingwokkitchen.com', '1592342743', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.oldesycamoregolf.com', 'https://mckinley.illinois.edu', None, 'http://www.yorktownshoerepair.com', '1592342759', 'http://www.superwash.com', 'http://www.mountainsideapartments.com', 'https://www.tireworks.net/locations/4700-w-craig-rd-north-las-vegas/', None, 'https://www.arizonafederal.org/', 'https://cocofreshtea.ca', 'https://www.241pizza.com/locations/pizza-delivery-Etobicoke-store-0061', 'http://alomdalounge.com', 'https://www.lnaservices.com', 'https://locations.wendys.com/united-states/az/avondale/900-north-99th-avenue', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://blueaspenmarketing.com', None, '1592342956', 'http://www.kingtutchmassage.com', 'http://rcornerdiner.com', None, None, 'http://www.citybuddha.com', None, None, 'http://www.tintgta.ca/', None, 'http://www.blairbbq.com/', 'http://giftsandgames.ca', '1592342994', 'http://www.sandalwoodspa.ca', 'http://www.theveganduchess.ca/', None, 'http://www.unosalonlv.com', 'http://www.longjohnsilvers.com', 'http://www.ellettlaw.com/', 'http://laflordecalabaza.business.site', None, 'http://thekingbar.com', 'https://shoto.momofuku.com', None, 'http://happybowlsaz.com', 'http://wyn.lv/AlexRestaurant', None, None, 'http://www.donandcharlies.com/?utm_campaign=yelp+profile&utm_medium=social&utm_source=yelp', 'http://carolinaprosweep.com', 'http://www.exclusiveflowerspeoria.com', None, None, 'http://www.williamsfreshcafe.com/924-dixon-road', 'http://hospicewestaz.com', None, None, 'http://www.mybigfatgreekrestaurant.com', None, 'http://www.mcgillrosegardenevents.com', 'http://www.eastcoastjoes.com', 'http://www.solonohio.org/217/Grantwood-Golf-Course', 'http://thelastwordcharlotte.com', 'http://www.cravingscu.com', 'http://eurosportphoenix.com', None, 'http://www.popinsaz.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'https://fabutan.com/locations/ontario/etobicoke/islington/', None, 'https://agents.allstate.com/jacque-riggs-chandler-az.html', 'http://www.busybeetools.com', None, 'http://hoofcocktailbar.com/', None, '1592343141', 'http://www.exhibitaffects.com', 'http://www.callclogbusters.com', 'http://britishauto.ca', 'http://hangarfoodandspirits.com', 'http://www.applebees.com/', None, 'https://www.spencediamonds.ca/location/mississauga-on/?utm_source=Yelp&utm_medium=Display', None, 'http://www.cltexpress.com', 'http://hornjohnsen.com', 'http://www.salondeelephant.com', 'https://norwindental.com', None, None, 'http://lasvegasmobiledetail.com', None, None, None, None, None, 'http://www.greatclips.com/salons/6225', None, None, 'http://hairimagespgh.com', 'https://www.kona-ice.com/local-site/kona-ice-pittsburgh-south/', 'http://www.agdpainting.com', 'http://www.clickchickphotography.com', 'http://angusone.com', None, 'http://www.doortodoor.com/default.aspx?src=yelp', '1592343209', None, None, 'http://www.nassauto.com', 'http://www.poolsbyyouinc.com/', 'http://www.flawlesslashspraytan.com', 'https://www.americanautoshipping.com', None, 'https://inkedmicrobladingparlor.com', None, '1592343230', 'http://bugweedmart.com/stores/phoenix', None, 'http://www.geaugaparkdistrict.org/parks/headwaters.shtml', 'https://www.bannerhealth.com/locations/goodyear/banner-urgent-care-1', 'http://www.thethriftking.com', None, 'http://www.paradigmperfauto.com', 'http://www.yogapura.com', 'http://www.dhanimalclinic.com', 'http://www.kinginsulation.com', 'https://stores.savers.com/on/vaughan/valuevillage-thrift-store-2110.html', 'http://www.kraftscreensaz.com', 'http://www.collegestreetbar.com/', 'http://www.drlamborndds.com', '1592343267', 'http://www.kinderbugs.com', None, 'https://www.petsmart.com/stores/us/az/gilbert-store1900.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://Www.arizonasixshooters.com', 'http://www.thewhiterabbitsalon.com', 'http://www.savvystagingaz.com', None, 'http://www.marriott.com/hotels/travel/clewl-residence-inn-cleveland-westlake/', None, 'http://www.VegasFlowers.com', 'http://www.glendalechildcare.com', 'https://www.josbank.com/store-locator/phoenix-az-771?utm_source=yelp&utm_medium=listing&utm_content=771&utm_campaign=AZ', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.frysfood.com/', None, 'https://www.carlifeautocare.com/service-locations/carlife-scottsdale', None, None, 'https://www.fjimports.com', 'http://www.aflyingcamera.com', 'http://www.azarcheryclub.com', 'http://www.bodynbrain.com/Durango', None, 'http://www.rackroomshoes.com', 'http://www.theartsmusicstore.com', 'http://www.whiplashcleveland.com', 'http://www.robjensen.com', 'http://www.fashionq1982.com', 'http://www.clarkcountynv.gov/Depts/parks/Pages/park-pebble.aspx', None, 'http://www.avonlakeeyecare.com/index.html', 'http://www.judithlieber.com', 'https://www.mywellcarepharmacy.com', 'http://www.americanpremierhhc.com', 'http://www.ultrapatios.com', 'https://myguysnow.com', None, None, 'https://www.cochranebenjaminmoore.com/crowfoot', 'http://www.petitautowash.com', 'http://www.countyofdane.com/lwrd/parks/yahara.aspx', None, 'http://www.thelibertycharlotte.com', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', 'http://rainbowcompany.org/', 'http://adiperry.com', 'http://maintainlv.com', 'http://www.redlinealarmcompany.com/', 'http://gloryofindia.com', None, None, 'http://www.cnsconstruction-nv.com', '1592343396', 'https://www.wyndhamhotels.com/hotel/15121?tel=18003291073&iata=00065402&cid=fe:di:20161220:yl:pp:dius:15121', None, 'http://indianrotihouse.com', 'http://www.alliancefloorsource.com', 'http://www.thepixelconnection.com', 'https://dutchbros.com/?utm_source=goodyear&utm_medium=yelp&utm_campaign=website_goodyear', 'https://johnsonsbarbershopverona.com', 'http://www.yourairconditioningandheating.com', 'http://aronsbarbershop.net', '1592343427', 'http://www.osteopathicmedicalassociates.com', 'http://www.sekaibeauty.com', 'http://www.starksbarbercompany.com', None, None, 'http://bigboysburgers.com/', 'https://local.biglots.com/oh/beachwood/5181?zcp=pd_local_yelp', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360198&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://qualitystarbenz.com', 'http://unlv.edu/veterans', 'https://taggartplumbing.com', 'http://www.heidelbergantiquemall.com', 'http://www.pfdepot.com', 'http://www.rykyoga.com/', 'http://www.oceanpalate.com', 'http://www.olapoke.ca', 'http://www.legendflooringaz.com', None, 'http://taketheflooraz.com/', 'https://whitebirchbarn.com', 'http://www.evovegas.com', 'http://www.nvmedicalcenter.com', 'http://stores.partycity.com/pa/pleasanthills/party-store-pc662.html', None, None, None, 'http://www.beautycreations.co', None, 'http://www.imperialpalace.com', None, 'https://locator.chase.com/nv/las-vegas/6460-sky-pointe-dr', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'https://www.autozone.com/locations/az/tolleson/2580-s-99th-ave.html', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', "https://www.brueggers.com/?utm_source=yelp&utm_medium=homepage&utm_campaign=pineville&utm_term=Bruegger's%20Bagels%20Home%20Page", None, None, 'http://www.fanexpocanada.com', None, 'http://oliverjewellery.ca/', 'http://www.silverdragonaz.com/', 'http://www.jpsrestorationandconstruction.com', 'https://www.shopfuego.com', 'https://www.hunter-everage.com/?npcmp=dir:local:4048366:28212', 'https://www.walgreens.com/locator/walgreens-2324+w+war+memorial+dr-peoria-il-61614/id=6408', 'https://malleys.com/stores/lakewood/', 'http://www.cornerstonestudio.ca', 'http://www.queenshead.ca', '1592343553', None, 'https://fhraz.com', 'http://www.z-teca.com', 'https://www.massagespategacay.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'http://actionrideshop.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.starbucks.com/store/10311/', 'http://zsfinejewelry.com', 'https://locations.churchs.com/az-phoenix-7235', '1592343582', 'http://www.floraldesignsbypaul.com/', 'http://www.funflick.com', 'https://budgetblinds.com/EastMesa/?utm_source=yelp&utm_medium=naf-listing&utm_campaign=NAF-LOCAL-YELP', 'http://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXTW', 'https://www.luckysliquor.com', '1592343595', 'http://www.tbaar.com', 'http://www.desertviewvisionnorth.com/', '1592343609', None, None, 'https://webshop.friendlystranger.com', None, None, 'https://ad.doubleclick.net/ddm/clk/459133854;262878939;f', None, 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://www.radisson.com/chandleraz', None, 'http://touchofalohallc.com', None, 'http://www.westsideskates.net', '1592343643', None, None, 'http://www.bk.com', 'http://prosciuttos.com', 'http://www.radisson.com', None, None, None, None, None, None, 'http://ledgewoodbarbershop.com/', 'http://www.rio-rancho-painting.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, 'http://www.bernardinsfinedining.com/charlotte', 'http://www.cgvegas.com', None, None, None, 'http://kotoramen.eat24hour.com', None, 'http://allproshadeconcepts.com', None, 'http://www.azisushi.com', 'http://myphoenixplumber.com/', 'http://www.pizzapizza.ca', '1592343716', 'http://www.tropicalsmoothie.com', None, 'http://curatiomassagelv.com', '1592343727', None, '1592343731', None, 'http://www.hortoncc.com', '1592343736', 'http://www.bromwichandsmith.com/calgary-area', None, None, None, 'http://www.yorktownestates.com', 'https://www.fuegomk.com', 'https://www.softsurroundings.com', 'http://www.PrecisionEyecareAZ.com', 'https://www.zonawyyerd.com', 'http://www.foodvillage.ca', 'http://loriswimschool.com/', 'http://www.waxonwaxoffbodywaxing.com', None, None, None, None, 'http://www.tasteofthailandcuisine.com', 'https://locator.chase.com/oh/lorain/115-w-21st-st', 'https://www.agentchriswing.com/?utm_source=Yelp%20CTA&utm_medium=Call%20to%20Action%20Click&utm_campaign=Yelp', 'http://www.tearalab.com', None, 'http://www.bobsbbqemporium.com', None, 'http://www.sandstonepm.com', 'https://redrock.sclv.com/Gaming/Bingo?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', None, None, None, None, 'http://www.carefreestone.com', 'http://www.eyediologyvisioncare.com', 'http://www.suresafestorage.net', 'https://www.nsbank.com/branch/?branch=durango_and_215_south_branch', None, 'https://www.davejonesinc.com', None, 'http://www.goodlifefitness.com', None, 'http://www.brueggers.com/', 'http://chiclavie.com', None, 'http://www.lasvegasmarket.com/the-pavilions', None, None, 'http://theatriumathenderson.com', 'http://fiveguys.com', None, None, 'http://www.bk.com', 'http://www.davidfranksalon.com', None, 'http://www.tarbells.com', None, 'http://www.sydneyafterdark.com', None, 'http://www.theolivetap.com/find-us/pittsburgh-pennsylvania/', None, 'http://www.cookout.com', 'http://www.arentwenaughty.com/', 'http://awsboats.com', None, None, 'http://gotosunshinecleaners.com', 'http://callitnewcallitantique.com', None, 'http://www.susieandwill.com', 'https://www.prestigeanimalclinic.net/?utm_source=yelp&utm_medium=social', None, None, 'http://www.autokeymasters.com', 'http://www.avintageaffair.ca', 'http://www.ostrichfestival.com/', 'https://www.walmart.com/store/2512/phoenix-az/details', 'http://www.lvcabs.com/', 'http://www.mainstdeli.com', 'http://www.azdoor.com', 'http://tutoringclub.com', 'https://www.wellsfargo.com/locator/bank/?slindex=3&il=EN', None, '1592343935', None, 'https://store.vioc.com/oh/kent/403-e-main-st-44240-060052', 'https://www.houseofwindowcoverings.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.pensketruckrental.com/locations/nevada/las_vegas/075610', None, 'http://www.familydentalcareofmedina.com', None, 'https://www.choicehotels.com/pennsylvania/pittsburgh/comfort-inn-hotels/pa354/rates', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.axethrowingcalgary.ca', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.getspun.ca/', 'http://www.vegasredroom.com', None, None, 'http://www.floodaz.com', 'http://www.hustlerhollywood.com', 'https://www.wyndhamhotels.com/hotel/27714?tel=18885951878&iata=00093785&cid=fe:mt:20170424:yl:pp:MTUS:27714', None, 'http://www.aupetitfour.com', 'http://wi.sunprairie.papamurphys.com/pizza_sun-prairie_wi_wi018.html#fbid=Q7yOP_LFToV', 'http://sunstopperslakenorman.com', 'https://www.nationalcar.com', None, 'https://www.parkfordtallmadge.com', None, None, 'http://www.cheuvronts.com', 'http://www.cedarsdavidson.com', 'http://www.fleetfeethuntersville.com/', None, None, 'http://apismead.com/', 'https://fiestahenderson.sclv.com/?utm_source=YELP&utm_medium=SOCIAL&utm_term=FH&utm_content=FH-PROPERTIES&utm_campaign=FH-YELP', 'http://fiveguys.com/', None, 'http://civillibertiesbar.com', 'http://shootpointblank.com/point-blank-cleveland/', 'http://uniquehd.com/', None, 'http://www.hcpnv.com/clinic/galleria/', 'http://www.theonion.com', 'http://www.weareonetherapy.com', 'http://www.northfieldvethosp.com', 'http://mimsburgershop.com/', 'https://www.walgreens.com/locator/walgreens-1159+e+southern+ave-mesa-az-85204/id=3670', '1592344059', None, 'http://www.brightonmusic.com/', 'http://www.clubpilates.com/arrowhead', None, None, None, 'http://www.bloorstreetdiner.com/', 'http://www.thespot-etc.com', None, 'http://www.speakgeekpcs.com', None, '1592344090', 'http://nailspa4u.com', 'https://thefoundryyoga.com/schedule-tempe-mesa', 'http://www.winnersma.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, None, '1592344108', None, 'https://www.fastsigns.com/108-airpark-scottsdale-az', None, 'http://www.iarepairaz.com', None, 'https://www.bankofamerica.com', 'https://www.connollysgrill.com', None, 'http://www.newlookuniversallv.com', 'http://www.gift-4-you.com', None, 'http://www.quiktrip.com', 'http://www.vanlierribbinkmd.com', 'http://www.starbucks.com/store/9334/', None, 'https://www.wingstop.com/location/wingstop-421-phoenix-az-85015/menu', 'https://tikkabistro.com', None, 'https://banking.nbarizona.com/blocator/viewLocationMap.html?recordId=206&latitude=33.48435&longitude=-112.072817', None, None, 'http://www.harkinstheatres.com/', 'https://www.gowireless.com/stores/az/gilbert/gilbert-gilbert-road/', 'https://locations.waxcenter.com/nc/charlotte/charlotte-arboretum-0169.html', None, 'http://mendocino.ca/', 'http://bairrada.ca', 'https://www.navyfederal.org', 'https://locations.sonicdrivein.com/nv/lasvegas/6301-w.-lake-mead-blvd..html', None, 'http://www.happy-lemon.com', 'http://www.whiskeydickslv.com/', '1592344192', 'https://www.peedoc.com/dr-roscoe-nelson', 'https://www.thebodyshop.com/en-us/?utm_campaign=us_180418_w19_search_bau&utm_medium=yelp&utm_source=yelp&utm_content=websiteurl', 'http://www.carterluxuryliving.com/?utm_source=Yelp&utm_medium=reputation', 'http://www.vortexrecords.ca', 'http://www.trinitysaloncharlotte.com', 'http://handymanmichael.com/', 'http://www.kingputtlv.com/las-vegas', 'http://www.bodyheattanning.com', 'http://www.oilpaintingart.ca', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.whitesquirrelcoffee.com/', None, 'http://www.onewayac.com', 'http://www.inspireyoga.ca', 'http://www.katsurdental.com/locations.php', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://ajsautoservice.com/', 'http://scootermopedrentallasvegas.com', 'https://www.bose.com', 'http://chase.com', 'http://vitasmart.net', None, 'http://yoshiburritos.wixsite.com/yoshi1', None, 'http://www.kellyautomotive.net', 'http://www.drzdentistry.com', 'http://www.mojoyogurt.com', 'http://www.csamco.com', 'http://hwy55.com', 'http://www.collinscooling.com', None, None, 'http://www.fritzlawyers.com', 'http://www.erasedlasertattooremoval.com', 'http://www.cox.com', 'https://www.sourceforsports.ca/en-CA/Stores/82-Just-Hockey-Toronto-Source-For-Sports.aspx', None, 'http://www.littlecaesars.com/', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.tristatevalet.com', None, None, 'http://www.phoenixgutter.org/', 'http://www.spotlesspools.com', None, 'http://travismathew.com', None, None, 'http://www.dvinewinecafe.com', 'http://www.cuyahogadogs.com/', 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://thelounge.social', 'http://arescuisine.com', 'http://advicefromacaterpillar.ca', 'http://www.officedepot.com', None, None, 'http://www.1stcb.com', 'http://www.dilworthtan.com', 'https://www.autoshopparma.com', None, 'http://www.macdonaldsranch.com', None, None, None, 'http://www.AprendeNV.com', None, None, 'http://www.rhodesranchgolf.com', 'http://www.weddingbellesaz.com', 'http://www.legendcleaners.com', None, 'http://www.azlivingtoday.com', None, None, 'http://www.polepositionraceway.com', 'http://www.1888junkquick.com', 'http://leisuredivecanada.com', 'http://www.dollar.com/Locations/gen.aspx?locationId=YTOC18', 'https://www.mycenters.com', None, 'http://www.babiesrus.com', 'http://Gdiinstal.wixsite.com', 'https://www.downtownvegaschapel.com', 'http://www.jackcarterchev.com', 'http://www.bpisite.com', 'http://www.mysunnypros.com', '1592344410', 'http://www.garagedoorservice.com', 'http://www.marathon.com', None, 'http://www.scottsdaleinstitute.net/', 'http://www.7-eleven.com/?yelp=29384', 'http://www.treeservicephoenix.net', '1592344425', 'http://www.rics-yyc.ca', 'https://www.sportchek.ca/stores/eglinton-corners.html', 'https://www.honorhealth.com/locations/specialty-care/honorhealth-bariatric-center?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-bariatric-center', 'http://www.costco.com/warehouse-locations/middleton-wi-1020.html', 'http://www.amatopizza.com/amato-pizza-yonge-st-college/', '1592344440', None, 'https://specialtysclv.com', 'http://bosadonutsaz.com', None, None, 'http://www.phoenixflowershops.com', 'http://www.hakkawok-aurora.com', 'http://kinkshair.com', 'http://www.giuseppesitalianmarket.com', 'https://www.chick-fil-a.com/avondale', None, None, 'http://mrgreek.com', 'http://leesliquorlv.com/locations/lake-mead-tenaya-2/', 'http://www.tablawinebar.ca/', 'http://goodcompanybarbers.com', None, None, None, 'http://www.zumiez.com', 'https://www.thenaillogic.com', None, 'http://www.steel-partners.com', '1592344495', None, 'https://www.nothingbundtcakes.com/bakery/nv/las-vegas-eastern?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=las-vegas-eastern_2', 'https://www.bmwofwestlake.com', None, 'https://www1.shoppersdrugmart.ca', 'http://www.sevenpalmsautomotive.com', 'http://www.diamondglassandmirrorinc.com/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.elementsofbodywork.net', 'http://www.upfronthauling.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://clickserve.dartsearch.net/link/click?lid=43700044281329004&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.umbergerperformance.com', None, 'http://www.scrapbooksbydesign.ca', None, None, 'https://woofstock.ca/', None, 'http://www.greyfriarspub.ca', 'https://www.scooterscoffee.com', 'http://radioshack.com', 'http://www.banfield.com/veterinarians/az/scottsdale/scd?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.eastdalemedical.com', 'https://www.mobiletechautoglass.com', 'http://safelite.com', 'http://www.curioustails.com', 'http://www.kellyslanding.ca', None, None, 'https://www.bestwestern.com/en_US/book/hotel-rooms.03160.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03160', 'http://www.meloautoto.com', 'https://www.amazinglashstudio.com/studios/pa/murrysville/murrysville', None, 'http://www.durangocanyon.com', 'http://cheyennetrailslv.com', 'https://www.greulichs.com', 'http://body-mechanix.com/Scottsdale-Old-Town#/today', None, None, '1592344587', 'http://www.croach.com/', 'https://www.dominos.com', 'http://www.univchiropractic.com/', '1592344598', 'http://www.ruralking.com/?utm_medium=yext&utm_source=not-gmb&utm_content=yext-rk-18', 'http://www.greenvalleyranchresort.com/?section=entertainment&page=whiskey_bar', 'https://www.autozone.com/locations/az/chandler/1025-n-arizona-ave.html', 'https://valleywisehealth.org/locations/community-health-center-mesa/', None, 'https://www.thedutchstore.ca', '1592344613', 'http://www.miraclemethod.com/', None, None, 'http://www.fantasticsams.com', '1592344626', 'https://www.fastmed.com/urgent-care-centers/monroe-nc-walk-in-clinic/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.lunavisionandmedspa.com', '1592344634', None, 'http://ninestoriespgh.com', 'http://doubletapconcealed.com/', '1592344645', 'http://www.tropicalsmoothiecafe.com', None, 'https://www.staples.com', 'http://www.timhortons.com/', 'http://www.sunrisechildrensdentistrylv.com', 'http://www.cityofhenderson.com/henderson-happenings/parks-and-trails/locations-and-features/tuscany-park', 'https://www.chick-fil-a.com/montrose', 'https://www.fastmed.com/urgent-care-centers/tempe-az-walk-in-clinic-asu/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'https://www.printden.com', None, 'http://www.blackstonecountryclub.com', None, 'http://www.wattscurrent.com', 'http://www.yourartparty.com', None, 'http://ww2.cox.com/business/arizona/home.cox?sc_id=nat_lbs_yp_biz_yelp-az3a_11q4', 'http://www.thecleverkoi.com', 'http://www.cliquephotostation.com', 'http://www.southparkcommons.com', 'http://www.thenutritionshack.com', None, 'http://www.meineke.com', 'http://www.calgarylabservices.com/', 'http://www.sallybeauty.com', None, '1592344706', 'https://curaleaf.com/stores/pl/curaleaf-pavilions-85035/', 'http://www.prairielanes.com', 'http://www.coffeeconecafe.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://locations.arbys.com/us/pa/pittsburgh/4810-mcknight-rd.html', 'http://www.ehostsystems.com', None, None, None, 'http://www.bajachuys.com', 'http://www.whiterosekitchen.ca', 'https://locator.chase.com/ca/sun-city/26750-mccall-blvd', 'https://www.radisson.com/toronto-hotel-on-m5j2n5/ontoront/?s_cid=os.amer-ca-rad-ONTORONT-gmb', 'http://tinytownvaughan.ca', 'http://www.fazioshairdesigns.com', 'http://www.rodworks.com', 'http://ad.doubleclick.net/clk;280858410;107462604;b', 'http://www.thetantanroom.com', None, 'https://www.scottsdaleinstitute.net', 'http://vitanya.com/scottsdale/', 'http://www.morganjewelers.com', '1592344760', None, 'https://www.purebarre.com/location/scottsdale-az', 'http://www.clemetparks.com/recreation/golf/washington.asp', 'http://www.northolmstedcjdr.com/', None, 'https://www.esso.ca', 'http://azquilts.com', 'http://elsombrero.ca/', 'https://www.chestnuthillsdental.com/practices/chestnut-hills-dental-monroeville/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'https://www.dominos.com', 'https://www.mcdonalds.com/us/en-us/big-mac-trio.html?cid=PS:GCM_MOP:NB::Yelp:All', 'http://www.1brotherspizza.com', 'http://www.sunsetspasaz.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=3248', None, None, 'http://www.themountaingrill.com', 'http://torontointernetcafe.com', 'http://www.dreyeman.com', None, 'http://www.rejuvenatemindbodysoul.com', 'https://www.menswearhouse.com/store-locator/4627?utm_source=yelp&utm_medium=listing&utm_content=4627&utm_campaign=IL', 'https://www.myeyedr.com/locations/independence-boulevard?utm_source=Yelp&utm_medium=Referral&utm_campaign=independence-boulevard', None, None, 'https://www.sephora.com/happening/stores/matthews-jcpenney-at-windsor-mall', 'http://www.vinestyles.ca', None, None, 'https://uptown.modoyoga.com', 'http://www.saskatoonfarm.com', None, None, 'http://www.nailsstation.com', 'http://sequoiarealty.com', 'http://activenevadachiropractic.com', 'http://www.yinzbreakifix.com', 'http://www.kitchenstuffplus.com', None, 'http://www.appalachiabbq.com', '1592344865', 'http://www.bostonpizza.com', 'http://www.rushstreetpizza.com', 'http://www.westcoastdealingschool.com', 'http://lavishbeautybar.com', 'http://www.maueranimalclinic.com/', None, 'https://agents.farmers.com/az/peoria/lucas-atwood?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.CreamberryLV.com', 'http://www.cascadelimo.com', 'http://www.cammusos.com', None, None, None, 'http://dineencoffee.com', None, 'http://www.kwiktrip.com/Locations/Details/832/', 'http://www.abelldermatology.com', None, 'https://www.kfc.ca/store/17295-leslie-street-newmarket', 'http://www.noobox.com/', 'https://www.hendersonmoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://www.barceloscanada.ca', 'http://www.rawlifefarms.com', None, 'http://www.milagrorestaurant.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://electric-needle.com/', 'http://www.pittsburghfloat.com/', 'http://www.thomasandthomasdental.com', 'https://maps.rbcroyalbank.com/locator/searchResults.php?t=6702', 'https://www.lifesourcewater.com/phoenix_yelp.php?utm_source=Yelp&utm_medium=web', None, None, 'http://www.drbeauchiropractor.com', None, None, 'http://sweetdreamswithlove.wix.com/sweet-dreams', 'https://www.mcdermottmotors.com', 'http://www.homedepot.ca/', None, 'http://www.americanapparel.net', None, 'https://modernpetsalon.com/ballantyne/', 'http://www.lovablepetsitting.com', 'http://www.fantasticsams.com', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.burritozone.ca', 'http://www.herculesindustries.com', 'http://signatureskincaremakeup.com', None, None, 'http://www.jenhenry.com/', 'http://www.childrensplace.com', 'http://www.youngthailand.com', None, 'http://www.innerradiancespa.com/', 'http://www.starbucks.com/store/9289/', '1592345016', 'http://www.theplazawr.com', 'http://www.marriott.com/hotels/travel/cltrn-residence-inn-charlotte-lake-norman', None, 'http://www.marmishoes.com', None, None, None, 'http://www.chpchospice.com', 'http://www.no1bobatea.us', None, None, 'https://www.frysfood.com/storeHours?store=66000069', None, 'http://sameclub.ca', None, 'http://www.pitapitusa.com/', 'http://www.lcbo.com', None, 'http://www.daryascostumes.com', 'http://www.virginmobile.ca', 'http://www.villagioapartmenthomes.com/', 'https://www.cash1loans.com/Locations/NEVADA/Las-Vegas-Cheyenne.aspx', 'http://www.disneyonice.com/treasure-trove', None, 'https://merchantandtrade.com/?utm_source=googlemybusiness&utm_medium=organic&utm_campaign=gbreferral', 'https://bikedepot.com', 'http://www.jcl.com/physician-network/practices/john-c-lincoln-your-family-medicine', 'https://www.dispatchhealth.com/locations/az/phoenix/?utm_campaign=localmaps&utm_medium=local&utm_source=yelp&utm_content=3', 'http://www.qualtechachtg.com', 'http://www.adamspaintingcle.com', 'http://mivip.com', None, 'http://www.pulsepeters.com', '1592345126', None, None, None, 'http://locations.atipt.com/henderson-nv-seven-hills', 'https://www.regenpainandwellness.com', 'http://charmeck.org/mecklenburg/county/ParkandRec/StewardshipServices/NaturePreserves/Pages/McDowell.aspx', 'http://pizzazzpizzeria.com/', 'http://www.salonzoya.xyz', 'http://www.lasvegasbabyequipmentrentals.com', 'http://hangar9az.com', 'http://www.howardhanna.com/', 'http://www.ttc.ca/Subway/Stations/Lansdowne/station.jsp', 'http://www.avonworthcommunitypark.org/', 'http://www.divinehealthacademy.com', 'http://www.pickwickandfrolic.com/', 'https://www.advantage.com/location/las-vegas-mccarran-intl-airport-las/?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_local', None, 'http://www.modelland.com', 'http://www.elpolloloco.com/locations/store/3855', 'http://www.dave-harry.com', 'https://locations.theupsstore.com/az/glendale/20118-n-67th-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.lotusdentalassociatesfortmill.com', 'http://www.concealedcarrycourses.com/', 'http://www.cypress-plumbing.com', None, None, 'http://www.weecansign.com', '1592345217', 'http://www.autobahncollision.com', None, 'http://www.canyondental.ca', 'https://www.divsouth.com', 'https://palmbeachtan.com/locations/NC/Harrisburg-North-Carolina-49/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=AUG', 'http://www.xcelcleaningservice.com/', 'https://locations.wendys.com/united-states/oh/urbana/734-scioto-st.', 'https://theogandf.com', None, 'http://www.cowboybobby.com', 'http://playerstravel.com', 'http://www.starbucks.com/store/9298/', 'https://www.localfirstaz.com/events/fall-festival', 'http://israelimartialartslv.com', 'https://www.wincofoods.com', None, 'https://vibe5fitness.com', 'https://goo.gl/oq2f2R', 'http://www.larkcreek.com/bolv.htm', 'https://www.trulynolen.com/location/nevada/las-vegas-pest-control?utm_source=yelp&utm_medium=listing&utm_campaign=', None, 'https://www.onehourheatandair.com/phoenix/', None, 'http://www.popalock.ca/pop-a-lock-of-mississauga', '1592345304', 'http://www.thatpotteryplacepittsburgh.com', 'http://www.dairytreats.com/cafesheli/info.html', None, 'http://www.charmeck.org/', 'http://www.arizonadigestivehealth.com/locations/glendale', 'http://www.bowsergm.com/?cs:pro=repman&cs:e=yelp', None, None, 'https://www.cinemark.com/pennsylvania/cinemark-galleria-at-pittsburgh-mills-and-imax', 'http://www.gnc.com', '1592345341', 'http://www.blackjackmopedsandscooters.com', None, 'http://www.northphoenixdental.com', None, None, 'http://www.thedump.com/Phoenix', 'http://www.marbellalv.com', None, 'https://www.cafebebida.com', 'http://www.sammysatplayhousesquare.com/', 'https://sugar-and-lace-bakery.business.site', 'http://www.mrtintinc.com', 'https://www.wirelesstoyzmesa.com', 'http://www.animalhospitalofmonticello.vetsuite.com', 'http://www.super-nerds.com', 'https://www.tacodelmar.com', 'http://www.cuttingboard.vegas', 'http://www.dirtylarrystopsoil.com', None, 'http://www.whiteheadmanor.com/', None, 'http://www.dinerdeluxe.com', 'http://vjazzywellness.com', 'http://carrington.edu/schools/las-vegas-nevada/?LeadSrcID=1176&AdvGroupName=Yelp&AdvCampaignName=YelpLasVegasFY17&AdvSource=Internet', 'http://www.hattielarlham.org/v/doggie-day-care-cleveland.asp', 'http://www.lindamodernthai.com', None, None, None, 'http://www.bowlavard.com', None, 'http://lolaslasvegas.com', 'http://lakeviewpatios.com', 'http://www.suncity-summerlin.com/', 'http://www.puppyboutiquelv.com', 'https://local.pharmacy.safeway.com/az/peoria/10641-w-olive-ave.html', None, 'https://cutncolorbyclassy.business.site', '1592345465', None, None, 'https://dryprosystems.com/?force_source=local_organic', 'http://guthriesofcleveland.com/', None, 'http://www.gnc.com', None, 'http://www.greatclips.com/', 'https://romas.pizza', 'http://www.beverlyservices.com', 'http://curiocollection3.hilton.com/en/hotels/arizona/boulders-resort-and-spa-curio-collection-by-hilton-PHXRSQQ/index.html?SEO_id=YELP-QQ-PHXRSQQ', 'http://www.wolfpacktattoo.com', 'https://www.springspreserve.org/visitor-information/divine-cafe.html', 'http://www.bounce-a-rama.com', None, 'http://www.metropetvet.com', 'http://shop.tuesdaymorning.com/store/830', 'http://www.carssuperiorauto.com', 'http://www.lightninglubeaz.com', 'http://cococochocolatiers.com', '1592345529', 'http://swishlv.com/', 'https://jeanetterosario200.wixsite.com/thelittlebohemian', None, 'https://www.carstar.com/locations/nc/charlotte-15346/', 'http://swmodularinc.com/', 'https://www.united.com', None, 'http://www.magicautosales.com/used-cars-for-sale-phoenix/', 'http://beltlinecannabiscalgary.com', 'https://kidsandcompany.com/locations/bloor/', 'http://therositasplace.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.crusttremont.com', 'https://handymanpros.us', None, None, None, None, None, 'http://www.ladolcepesca.com/', 'http://bikemastersaz.com/', 'http://www.moodscanada.com', None, None, 'http://potliquorcas.com/', None, None, 'http://www.davescosmicsubs.com', 'https://www.nofrills.ca//store-locator/Dickie%27s+NOFRILLS+Newmarket/3621?storeId=3621', 'http://opalstudio.ca', 'https://www.famousfootwear.com/?partnerid=YELP', 'http://www.natn-az.org/cup-okarma', 'http://www.vegascheeburger.com/', 'http://www.ihg.com/staybridge/hotels/us/en/calgary/yycba/hoteldetail', 'https://www.pongratzop.com', 'http://www.restaurantchezgerard.com', None, '1592345622', 'http://whatthehellbarandgrill.com', 'https://www.clubpilates.com/northgilbert', 'http://www.metroc.ca', 'https://www.mandalaybay.com/en/restaurants/hazel-coffee-and-cocktails.html', 'http://thrandco.com/', 'http://www.bandofbarbells.com', 'http://sobyseatery.com/', 'https://nail-therapy-beauty-boutique.business.site', None, 'http://www.bedbathandbeyond.ca', 'http://www.amica.com', None, 'http://halfarplumbing.net', 'http://limosarizona.com', 'http://vangoghgrillbar.ca', 'http://www.majorpowersports.com', 'https://prayersfrommaria.org', 'http://www.marriott.com/hotels/travel/phxps-springhill-suites-tempe-at-arizona-mills-mall', 'https://locations.dennys.com/AZ/YOUNGTOWN/248555', '1592345668', None, None, None, 'http://www.larrymillerhyundai.com', None, 'https://theresortatsummerlin.com/dining/casual-dining/shizen/', 'http://www.justfalafel.com', None, None, 'http://www.ecowaterservisoft.com', 'https://countrybrook.mgproperties.com', 'http://www.ninamichellesalon.com', 'http://www.craftcitysocialclub.com', None, 'http://stylesuite35.com', None, 'https://petermanlumber.com', 'https://www.dollartree.com/locations/az/glendale/4709/', 'https://www.petsuppliesplus.com/Store/OH/Solon/Solon/98?utm_source=Yelp&utm_medium=Store-Page%C3%8A', None, 'http://www.fullservicerv.com', 'http://www.ufcgym.com/matthews', 'http://www.prettyuglybar.com', 'http://thirstynomadbrewing.com', None, 'http://www.eikonhair.com', 'http://frysfood.com', None, 'http://www.chosen-vintage.com', 'http://www.unlvino.com', None, None, None, None, None, 'http://badasscoffeelv.com', None, None, None, 'http://swjunkies.com', 'https://local.fedex.com/pa/pittsburgh/office-2064/', None, 'http://drakecommissary.ca', 'http://summerlinpediatricdentist.com/', 'http://www.mccleveop.com', 'http://www.tropicalsmoothiecafe.com', 'http://www.trueresilienceims.com', 'https://www.klinkecleaners.com/locations/dane-county-locations/monroe-street', 'https://www.crunch.com/locations/mississauga', 'http://www.unleasheddogs.net/', None, 'https://www.fuzzystacoshop.com', 'http://www.ljsilvers.com/', 'http://www.CrucialDataRecovery.com', 'http://www.stickyfingers.com', 'http://us.fruits-passion.com/', 'https://mcgrathspielberger.com', 'http://www.TheJasonDawsonTeam.com', 'http://www.dishitout.net/', 'http://www.qdogstudio.ca', 'https://www.minus5experience.com', 'http://www.madmotorsofmadison.com', 'http://formula-euro.com', 'http://muttsandcats.com', None, 'http://www.marathon.com', 'http://www.streeteatsaz.com', None, 'http://banksoreck.com', 'http://www.srfamilydental.com', None, None, 'http://www.adamwadehair.com', 'http://www.salonpiperglen.com', None, None, 'http://www.labellebayspa.com/contact.html', None, 'http://www.charlottehair.com', 'http://www.blueagavemexicancantina.com', 'http://www.eazorauto.com', 'https://lasvegassoccerstore.com', 'http://www.yesofcourse.com', 'http://www.craftsmancourt.com', 'http://www.verizonwireless.com/stores/ohio/north-olmsted/north-olmsted-201970/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.wallerbears.com/', 'http://www.greatclips.com/salons/3063', None, 'http://spastation5.com/', 'http://www.chevron.com', 'http://www.ruidosoremodeling.com', 'http://www.marceklawlasvegas.com/', None, None, 'http://www.valleyxpress.com/', None, None, 'http://turtlebacktrailers.com', 'http://www.dineoncampus.com/jwcharlotte', 'http://www.dunkindonuts.com', 'http://www.acehardware.com/store-details/03028', 'https://www.homedepot.com/l/Gastonia/NC/Gastonia/28056/3606?cm_mmc=seo-yelp&', 'https://www.thejoint.com/arizona/peoria/arrowhead-towne-center-48015', '1592345888', None, 'http://www.starbucks.com/store/15887/', None, 'http://alldogsgotobrenda.com/', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=244', 'http://www.joshandjenphoto.com', None, None, None, 'http://redcarpetmovingcompany.com', 'http://www.mythicalfabrications.com', None, 'http://www.barburrito.ca', None, 'http://www.skylinehelicoptertours.com/', 'http://www.fivebelow.com', 'http://www.themarlowapts.com', None, 'http://www.zxfitness.com/matthews', None, 'http://www.atties.net', 'http://www.bamburgheyecare.com', None, 'https://ganemjewelers.com', None, 'http://woodenrobotbrewery.com/', 'http://stores.homedepot.ca/on/vaughan/home-improvement-vaughan-on-7253.html', 'http://www.lapetite.com/your-local-school/las-vegas-nv-7300/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://www.thepathoffulfillment.com', None, 'http://www.richscigars.com', 'http://www.scottsdaleautogallery.com', 'http://www.tibuild.com', None, None, 'http://www.hanjigifts.com', None, 'http://www.tanizakaya.com', 'http://alterationslasvegas.net/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'https://www.summitcreditunion.com/?utm_medium=location&utm_source=yext', 'https://sunlifeorganics.myshopify.com', 'http://www.torontolimos.com', 'http://www.7-eleven.com', 'http://www.einsteinbros.com/', None, '1592346000', 'http://priorityrealty.net/', 'https://www.foodforthoughtdeli.com', 'http://www.goodlifefitness.com/locations/ontario/northyork/don-millseglinton?source=yelp-websitelink-northyorkdon-gl', 'http://www.switchbackcyclery.ca', None, 'http://www.churchs.com', 'https://www.hyatt.com/en-US/hotel/wisconsin/hyatt-place-madison-downtown/msnzd', 'https://mollybrownscuyfalls.com', 'http://www.organicbeautybar.ca/index.html', None, None, 'http://horseandhoundsportsgrill.com', 'http://www.healthcoachaz.com', 'http://www.juanitasbakery.com', None, None, '1592346044', 'http://www.fleetfeetpittsburgh.com', None, 'http://www.dobsonbaychiro.com', 'https://scottsdalehorizon.mgproperties.com', 'http://www.sammysbeachbarandgrill.com', 'http://batchtoronto.com', None, 'http://gangstercheese.ca', 'https://www.mfa.net/center/huntersville-health-rehabilitation-center', None, 'http://www.bk.com', None, 'https://www.arrowheadsigncompany.com', 'http://locations.avis.com/us/nc/charlotte/clt.html', None, None, 'https://www.iobx.com', 'http://www.bunkerfuneral.com', 'http://www.thelodgeatarrowhead.com', 'http://www.mattressfirm.com/', 'http://www.scottsdalehorseandcarriage.com/', 'http://www.meritusaz.com', 'https://www.cash1loans.com/Locations/ARIZONA/Glendale-Union-Hills.aspx', 'http://thebarefootforge.com', 'http://www.phxbluefin.com/', 'http://www.ccsocialkitchen.com', 'http://www.scrubsstation.com', 'http://www.affiliateddentists.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.omescape.ca', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592346124', 'http://www.sindebad.ca/', None, 'http://www.calgarysbestpubs.com/kilkenny', 'http://www.broadcastrentals.com', 'http://www.allstoragevegas.com/locations/nevada/lake-mead/?lid=2', None, 'http://www.ketzalmexicangrill.com', 'https://www.calranch.com/las-vegas/store-info', 'http://centennialhillsdentist.com/', 'http://www.petvalu.com', None, 'http://www.tamhoa.com', None, None, None, 'https://saanayoga.com', None, None, 'http://www.toysrus.ca', None, None, None, 'http://www.keyinnmacedonia.com', 'http://www.galitoschicken.com/locations.php', None, 'http://aaa-garage-door-repair-sun-prairie.business.site', 'http://morrisonvein.com/', 'http://www.reevesautowrecking.com/', None, None, None, None, 'http://www.loungeeighteen.com', None, None, 'http://www.mummasburritos.com', None, 'http://www.europeanbeautytoronto.com/', 'http://www.bobslocks.us', 'http://delfriscosgrille.com/location/phoenix/', 'http://www.shutterzinc.com/', 'http://valleyendodontic.com/#utm_source=VYRL&utm_medium=Yelp&utm_campaign=main', None, 'http://atozpaintinganddecorating.com', None, 'http://verona.sites.toronto.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'https://fingerprintinglasvegas.com', 'https://www.petsmart.ca/stores/ca/ab/calgary-store1201.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', None, 'http://www.midviewpizza.com', 'http://www.georgemadrid.com', 'https://www.originaljoes.ca', 'http://www.magurapizzeria.com', 'http://www.brasstackshoerepair.com', 'http://www.pickeringhonda.com/', 'http://www.myvegasbakery.com', None, '1592346282', None, None, 'https://redrock.sclv.com/Hotel/Pool?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.centerfoldsaz.com', 'https://www.purebarre.com/location/henderson-nv', None, 'http://www.ftilasvegas.com', 'http://www.caraudioaz.com', None, None, None, 'http://www.juicebaratlvac.com', 'http://www.doblowdrybar.com', 'http://www.villageofbaxter.com', 'http://www.callprobest.com', 'http://www.adobodragon.com', 'https://www.homedepot.com/l/Cave-Creek/AZ/Phoenix/85022/480?cm_mmc=seo-yelp&', 'http://www.itsugar.com', 'http://legionbrewing.com', None, 'https://locator.chase.com/oh/akron/50-s-main-st', 'http://isaacmoore.synergysir.com/eng', 'http://www.drteddysim.com/about-dr-teddy-sim/', 'http://libertygreensaz.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.laurelgyn.com', 'http://www.lasermedicalclinic.com/', None, 'http://www.marcos.com/locations/oh/mayfield-heights/mayfield-road?s=true', None, 'http://www.lymphatichealingcenter.com', 'http://www.valleymetro.org/about_valleymetro', 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-arcadia-100?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-arcadia-100', 'http://www.premahealth.ca', None, 'https://www.winners.ca', 'http://www.prantlsbakery.com', 'http://taylorhplumbing.com', None, 'http://dkhomeloans.com', 'http://www.jennyshairdesign.ca/', 'http://www.starbucks.com/store/9334/', 'http://www.bestmatt.com/', None, None, 'http://www.vaporiselv.com/', 'http://www.regentsquarerentals.com', 'http://www.jenlucasphotography.com/', 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', 'http://www.landscapingpainesville.com', 'http://www.coolairnowlv.com', 'http://www.polefitnessstudio.com', 'http://www.tonisober.com?cmpid=BX09_BLM_0006', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=10538&localechange=1', 'http://www.goldenacre.ca', None, None, 'https://advautoglass.com', '1592346449', 'http://www.uhpwarranty.com', None, None, 'http://www.bubbysbagels.com', 'http://www.arizonaappliancerepair.biz', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/22909+Emery+Road-Warrensville+Heights-OH-44128/storeid=7371?cid=ps_ylp_2020', None, None, 'http://www.clevelandphoto.org', None, '1592347449', 'http://www.LibertyMutual.com/Jarrett-Christianson', 'http://www.jnklandscapingandpools.com', None, 'http://www.phoenixazinjurylaw.com', 'https://www.goodguysphx.com', 'http://www.diamondappliancewisconsin.com', 'http://genosgiantslice.com', None, 'http://www.ANICindyKAgency.com', 'http://www.fye.com', 'http://www.quiktrip.com/', 'http://www.ultimatelasertag.ca/', 'https://www.aria.com/en/restaurants/catch.html', 'http://www.lasvegastire.net', None, None, None, 'http://www.allstoragevegas.com/locations/nevada/north-valley/?lid=8', 'http://www.disndatauto.com', 'https://www.gatorbacktreeserviceeastlake.com', 'https://www.sprint.com/storefronts/bd/sprint-las-vegas-nv-89119-fcs-748/?ecid=SEO:Yelp:2020_Q1:LastMile', None, 'http://www.casamaroc.ca', None, None, 'https://www.moonvalleynurseries.com/locations/mesa?utm_campaign=yelp&utm_source=yelp-az&utm_medium=mesa', 'http://www.baodingsouthpark.com', 'http://www.betterdog.com', 'http://www.hiprestaurants.com/', 'http://www.giantlasvegas.com', 'https://www.peoriaaz.gov/riovista', None, 'http://www.sandunyspa.com', 'http://christyslanding.com', 'http://www.campbowwow.com/phoenix', None, 'http://www.arcadepizza.com', 'http://www.empiremetalproducts.com', None, 'http://www.floordesignsflooringamerica.com', None, 'http://www.tpclv.com', 'http://www.thefoothillsgc.com', 'http://lacasapreschool.com', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/etobicoke-kipling-ave-c236.html?mcid=iyp:8368400', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://www.goliathtattoos.com', 'http://www.serviceking.com/locations/service-king-75th-ave?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', None, 'https://acupuncture-etc.com', 'https://www.appliancepartscompany.com', None, None, '1592347622', 'http://www.a1pizzawings.com', 'https://www.wellsfargo.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006430791762&ds_s_kwgid=58700000444978102&ds_url_v=2', 'http://www.laurafial.com', None, None, None, 'http://movingdonelight.com', 'http://mayfieldsmokeshop.com/', 'http://www.taqueria-los-altos-charlotte.com', 'http://www.dryerventexperts.ca', 'http://www.JimmyJohns.com', None, 'http://www.leroysautotruck.com', 'http://stretchthrift.ca', 'https://www.atyourdoorlv.com', 'http://www.angelsintheatticestatesales.com', None, None, 'http://www.wholefoodsmarket.com/stores/toronto', 'http://www.mallingereyecare.com', 'http://www.ahwatukeegolf.com', 'http://www.rivierabakery.ca', 'https://beyond-rehab-health-center.business.site', 'http://www.galleryofshades.com', None, 'http://www.stickyiggys.com', 'http://www.dolcegelato.net', None, 'http://www.murphyteamdreamhomes.com', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.ilovelavish.com', None, 'http://www.klugplumbing.com', 'http://enailsspascarborough.com', 'http://www.airmiles.ca', 'https://www.jamba.com/nc/charlotte/charlotte-douglas-int-l-airport-613', 'http://www.canonita.net', None, None, None, None, 'https://tools.usps.com/go/POLocatorDetailsAction!input.action?utm_campaign=yext&locationType=po&utm_source=google-my-business-url&locationTypeQ=po&radius=20&locationID=1376256&utm_medium=search', '1592347738', 'https://www.supercuts.com/locations/pa/castle-shannon/castle-shannon-center-haircuts-80838.html', 'http://www.pfchangs.com/', None, 'http://desertshoresnv.pilera.com/page/home', None, None, None, None, 'http://premiersolar.com', 'http://www.collectorsmarketplace.com', 'https://locations.cox.com/oh/fairview-park/3036-westgate-mall.html?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q2', None, None, None, 'http://www.woodcyclerefinishing.com', None, None, None, 'https://bradsmithroofing.com', None, 'http://www.noahhelps.org/venadovalley', 'http://www.bk.com', None, 'https://piedmontfarmersmarket.com', 'http://www.countryhillscollision.ca/', 'http://www.xstylephotobooth.com', 'http://www.mckibbinsirishpub.com/vaudreuil.asp', 'http://www.mebymichelle.biz', 'http://www.eclecticrevival.com', 'http://redwineandbrew.us/chesterland/', 'http://www.speedybrotherstransport.com', None, 'https://www.vivint.com/ppc/protect?exid=207432&utm_source=yelp&utm_medium=display&utm_campaign=yelp_q3&utm_content=ro5z1tILXj0GjK19Ts1fhQ', 'http://emidioandsons.com', None, 'http://www.abyssiniarestaurant.ca', 'http://www.timhortons.com', None, 'http://highergroundtoronto.com', None, None, 'http://www.pasdedeuxchildrensboutique.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.burgerim.com/our-locations/mentor/', 'http://villagepubcasino.com', None, 'http://www.customhide.com', 'https://soulsimages.wixsite.com/website-7', '1592347846', '1592347849', 'https://onceinteractive.com', 'https://www.waggingtailsaz.com', 'http://www.alflahertys.com/', 'http://www.freshmillions.com', 'http://www.pediatricdentistryofmatthews.com', None, 'http://www.atsudental.com', None, 'https://www.truliantfcu.org', None, 'http://www.allaboutkidspediatrics.net/', None, None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.barchef.com', 'http://www.caringforfamilies.com', None, None, None, 'http://www.hotelmortagne.com', None, 'http://www.gibbys.com/sauveur.php', None, None, 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=626&utm_content=bpas', 'http://www.kristihenigar.com', 'http://www.big5sportinggoods.com', 'http://www.jackinthebox.com', 'http://www.sprucemeadows.com/', None, '1592347929', 'http://www.redroomcafe.net', 'https://www.regions.com/Locator/Branch/bank-branch-Eastover-Charlotte', None, 'https://hollywoodkidsacademy.com/', 'https://www.thevegandoughnutco.com', 'http://www.paraisoskincare.com', 'http://www.mikesrigatonibistro.com', 'http://www.autozone.com', 'http://www.TNGphoto.com', 'https://www.maryslasvegas.com', 'http://www.passionofpersia.com', 'http://www.arizonafederal.org', 'https://hamletretirement.com', None, 'https://whizkidzplayland.com', 'http://www.hawthorninteriors.com', None, 'http://gelnailsbynoelle.com/', None, 'http://spiritapothecary.com/info.html', 'http://www.fashionxc.com/', None, 'http://www.hcpnv.com', None, 'http://www.dontcallmecupcake.com', None, 'http://www.springdespa.com', 'https://locations.panerabread.com/oh/north-olmsted/26086-brookpark-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', None, 'http://www.ikraspa.com/', 'http://www.intouchwellnesscenter.com', 'http://www.2thedeals.com', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://www.wokoflifepgh.com', 'http://www.boardwalkfries.com', None, 'http://cuppa-tea.ca', 'http://pulmonarylasvegas.com', None, 'http://psychicsofscottsdale.com', 'https://www.vitalmobility.ca', 'http://www.steaknshake.com/locations/24207-steak-n-shake-ridge-road-parma', 'http://www.flooringaz.com', 'http://www.stuttgartsouthwest.com', 'http://www.bashas.com/Locations.aspx?city=Carefree', 'http://www.bestinshowlv.com', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=phxno&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', None, 'http://www.mactaggartsmarket.com', 'https://www.fuddruckers.com/las-vegas-grand-canyon-mall', 'http://www.smilebyhanachi.com/gastonia-office', 'http://www.theanimalclinic.ca/', None, 'https://www.publicstorage.com/arizona/self-storage-phoenix-az/85027-self-storage/1113?pid=wyelp&CID=1245&CHID=AFL', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://aoa.md', '1592348069', 'http://fastfix.com/ourstores/metrocenter/', 'http://www.barrowbrainandspine.com', 'http://www.rayspizzahappyvalley.com', 'http://chewchew.net/', None, 'http://www.artifactlv.com', None, '1592348089', 'http://www.naturopathicvitality.com', 'https://www.durangodentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, None, 'http://www.riverside-wine.com/', 'http://www.napavalleyresources.com/index.html', 'http://www.rotate.com', 'http://www.paintcoloursunlimited.com', 'http://www.firstclassautoservice.com/', None, 'http://www.ladyjanehaircuts.com/ohio.html', 'http://www.petzore.com', 'https://locations.massageenvy.com/pennsylvania/gibsonia/5375-william-flynn-hwy.html', 'http://allergypartners.com/nevada/', 'http://bk.com/', 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', 'http://coffeetree.com/portfolio/shady-side/', 'http://www.DrizinLaw.com', 'https://www.marriott.com/hotels/travel/cltwr-residence-inn-charlotte-steele-creek/', 'http://www.shapesbrowbar.com/', 'http://mobilelocksunlimited.com', 'http://Shopwellsuited.com', 'https://www.gymboreeclasses.com/en/locations/NV/Summerlin/?utm_campaign=Summerlin&utm_medium=website&utm_source=Yelp&utm_content=yelp+page', None, None, 'https://www.vacuumcleanershoptempe.com', None, None, 'http://mercuriosgelatopizza.com', 'https://www.coulternissan.com', None, None, 'https://www.hungryhowies.com/store/hungry-howies-00813?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00813&utm_content=Website_Link', None, 'http://LeeSalonAZ.com', None, 'http://www.goodlifefitness.ca', 'http://mesacc.edu', None, 'http://www.dslrworkshops.com', 'http://www.miradordental.com', None, 'https://locations.massageenvy.com/ohio/beachwood/2101-richmond-road.html', 'http://homesteadsgrillandtaphouse.com', 'http://www.torontohydro.com', None, 'http://www.liveatvidalasvegas.com', None, 'http://mrsub.ca', None, 'http://www.promise-phoenix.com/', 'http://www.redmangousa.com', 'http://www.swisschalet.com', 'http://storelocator.pepboys.com/pepboys/stores/scottsdale/scottsdale/00684', 'http://shinobudiego.com', 'http://www.eyelashextensionsaz.com/', 'https://mikaku-izakaya-toronto.business.site', None, 'http://www.arizonapetsitting.com', '1592348224', 'https://pennies.bar', 'http://www.greathousehomerepairs.com', None, 'http://www.taipeisouth.com', 'http://www.advantagefunerals.com/en-us/locations/maryvale.page', 'https://www.e-zrentacar.com/location/montreal-airport-yul/', 'http://theschoolfinedining.com/', 'http://www.sushiomigoto.com', 'http://www.gymsport.com', None, 'http://www.donwayford.com', 'http://www.F8imagestudio.com', None, None, None, 'https://www.blakecapitalcorp.com/apartments/wi/madison/lincoln-ridge-apartments/', 'http://www.ontariochryslerjeep.ca/', 'http://www.dunkindonuts.com', 'http://www.dannyssalon.com', None, 'http://psychojock.com', '1592348277', 'https://www.extraspace.com/storage/facilities/us/pennsylvania/pittsburgh/300062/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.kidiatricdental.com/', None, 'http://www.sapphirepoollv.com', 'http://www.starbucks.com/store/9334/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.gamenestlv.com', 'https://www.mystudentvillage.com/us/illini-tower/', None, 'https://www.chosunnara.com', 'http://www.onsitecleaning.ca', None, 'http://www.brynmawrapartments.com', 'https://hottubhub.com', None, 'http://azroofing.com/', 'http://www.rockgardenfarms.ca', 'http://www.pitaikram.com', None, 'http://www.MySausageBuddy.com', 'http://pinecrestcadence.org', None, 'http://www.dollarama.com', 'http://chineseexpresstakeout.com', None, 'https://www.chezlouloucremeglacee.com', 'http://www.whitbymazda.com/', None, 'https://locations.waxcenter.com/az/scottsdale/scottsdale-mcdowell-mountain-0008.html', 'http://www.rolandssalon.com', 'http://www.greygoatpub.com', 'https://www.appliancepartscompany.com', None, 'https://www.bannerhealth.com/services/sleep-disorders?locationname=banner+university+medical+center+phoenix', 'http://www.tacville.com', None, 'http://www.dontortaco.com', 'http://www.parkviewdentaltoronto.com', 'http://www.grandconstructionphoenixaz.com', 'http://www.pepperpalace.com/', 'http://www.jacqueshome.com', 'http://www.enzorossisalon.com', 'http://www.sarkujapan.com/#home', None, 'https://www.deepwaterscleaners.com', 'https://stores.mooresclothing.com/ab/calgary/415---3545-32nd-ave--ne.html?utm_source=yelp&utm_medium=listing&utm_content=41&utm_campaign=AB', 'http://gastoniabuffet.com', 'https://store.vioc.com/pa/pittsburgh/4469-ohio-river-blvd-15202-060069', 'https://www.mrrooter.ca/toronto', 'http://agency.nationwide.com/agent/jesse-moreno-021132611-02003261100000', 'http://www.spinolasbakeshop.com/pages/index.html', 'http://www.quiltzonline.com', 'http://nevadanailstudio.com', None, 'https://www.livingwellnessmedicalcenter.com', 'https://beddingtondentalclinic.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.rawmorecafe.com', 'http://greatvegasbeer.com/', None, None, 'http://www.mlfchildrenstherapy.com', '1592348439', 'http://kidtokid.com/chandler', None, 'http://www.cleanatthecleaners.com/tegacay.html', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, None, 'http://www.triumphpropertymanagement.com', None, '1592348457', 'http://www.AZSnapIt.com', 'http://www.mathnasium.com/chandler', 'http://www.salonboutique.net/', 'http://www.onohawaiianbbq.com', 'http://www.azcosmeticdental.com', 'http://www.fat-tuesday.com', 'http://www.deserthighlandsscottsdale.com/', 'https://www.actionsportsperformance.net', 'http://www.dollargeneral.com', None, 'https://www.confinedescaperoom.com', None, 'http://www.vegasnightlifecrawl.com', 'http://www.barnesandnoble.com', None, None, 'http://www.heatshieldwindowtinting.com', 'http://www.whitemountainhealthcenter.com', None, 'http://sweetandsassycakes.blogspot.com/?m=1', None, None, None, 'https://european.ca', 'https://www.enterprise.com/en/car-rental/locations/us/ny/hudson-24hs.html?mcid=iyp:8368400', 'http://www.yogagrove.ca/', 'http://www.ananekebeautysalon.com', None, 'http://www.charlottemusic.net', 'https://vegashotairballoonrides.com', 'http://www.cmartintrucking.com', None, 'http://www.my-bluesky.ca', 'https://www.mercedesbenzofwilloughby.com', 'http://www.sobeys.com/en/stores/sobeys-ajax/', 'http://www.esthershobby.com', 'http://www.einsteinbros.com', None, None, 'http://www.jdmland.com', 'http://calgary.cnty.com/', None, 'http://www.cidercorpsaz.com', 'http://www.antiquitieslv.com', 'http://www.arcadiawellnesscenter.com', None, 'https://www.bjs.com/cl/willoughby/0096', 'http://www.bluemountaincleaners.com', '1592348570', 'http://www.cornerstonefamilymed.com', 'https://www.allstateselfstorage.com/self-storage/cave-creek-85331/', 'http://theusualplace.vegas', None, 'http://locations.crocs.com/az/tempe/10000057/', None, 'https://cacao70.com/fr/nos-emplacements/atwater', 'http://dominickssteakhouse.com/', '1592348591', 'https://www.cabofishtaco.com/ballantyne', 'http://www.aeeaz.com', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/mississauga-dixie-automall-c221.html?mcid=iyp:8368400', 'https://www.signaturestyle.com/locations/oh/ravenna/best-cuts-ohio-retail-center-haircuts-60700.html', None, 'http://www.fluffytailspetsalon.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Scottsdale-AZ-85260/822031/', None, 'http://www.noahhelps.org/locations/midtown/', None, 'https://www.wyndhamhotels.com/hotel/08737?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seca:08737', 'https://pureandsimple.ca', None, None, 'http://chill-restaurant.business.site', 'https://www.discounttire.com/store/nc/charlotte/s/1510?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.arbys.com', None, None, 'http://www.tastyhut.ca', 'http://www.phillycorner.com', 'http://www.rangelandrv.com', 'http://nc.publix.com', 'http://www.barsmart.com/VastaLounge/', '1592348647', '1592348650', 'http://labcorp-locations.com/arizona/mesa/21743.html', 'https://www.walgreens.com/locator/walgreens-22401+lake+shore+blvd-euclid-oh-44123/id=3312', None, 'http://www.propellercoffee.com', 'https://www.publicstorage.com/ohio/self-storage-akron-oh/44310-self-storage/1157?pid=wyelp&CID=1245&CHID=AFL', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.surpriseford.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', '1592348668', 'http://www.dreamcarrentals.com/', 'https://www.jerseymikes.com/9016', 'http://chachis.ca', '1592348677', 'http://www.drpirani.com', None, 'http://www.hotrodtattoo.com/', 'http://beautyconnectioncalgary.com', 'http://www.vaporlyfe.ca/', None, 'http://www.terribleherbst.com/', 'http://www.seautoexchange.com', 'http://www.metalheadmotorsports.com', 'http://eastvalleysports.com/', None, None, 'http://www.bjstampsandcoins.com/', 'https://www.dundasvethospital.com', 'https://www.preflightairportparking.com/reservation/phx/phoenix-sky-harbor/airport-parking/1', 'http://www.thephoenician.com/thirsty-camel-lounge/', 'http://organizecreatedecorate.com', 'http://www.couscousdtlv.com', 'http://www.completeautophoenix.com', 'https://www.circlek.com/store-locator/us/guadalupe/1619-w-baseline-rd/2706646', 'http://www.yellowgazeboclinic.com', None, 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=1', '1592348732', 'http://thekensingtonlodge.tumblr.com/', None, 'http://www.jasserim.com', None, 'http://www.lasikplus.com/location/pittsburgh-lasik-center?encSource=12149&utm_medium=Paid-Search&utm_source=Yelp&utm_campaign=Pittsburgh', None, None, 'http://www.patsrun.com', None, None, 'http://www.claires.com', None, 'http://www.coatedusa.com', 'http://www.eggsmart.ca', 'https://www.gymboreeclasses.com/en/locations/AZ/Glendale/?utm_campaign=Glendale&utm_medium=website&utm_source=Yelp&utm_content=yelp+page', 'http://www.sundevilauto.com/locations/az/mesa/east-mesa-power-26', None, 'https://milios.com', 'http://www.protectamerica.com/shop/order-package?agent=A11117', 'http://www.unclerayskis.com', None, 'https://www.olivegarden.com/locations/nv/las-vegas/las-vegas-cheyenne-ave/1363?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:las-vegas-nv-1363_pl:locurl_rd:1274', None, None, None, 'http://www.banfield.com/veterinarians/az/phoenix/pho?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://www.wildflowerbread.com/location/crown-coming-soon/', None, 'http://www.mysticmassageandwellness.com', 'https://www.costco.ca/warehouse-locations/anjou-qc-506.html', None, 'http://www.righthonda.com/', 'http://www.likenootherac.com', 'https://www.ljmacarons.com', 'http://www.barneon.ca/', 'http://americangypsycafe.com', 'http://www.southcharlottelifestyle.com/', None, None, 'http://spinesurgeryaz.com', 'http://www.pghbottleshop.com', 'http://www.ichidon.ca', 'https://www.americancountertopsandfloors.com', None, 'http://www.marbleslab.ca', None, None, 'http://www.firedpie.com', 'http://www.therollhouse.com/parma', None, 'https://www.athome.com/store-detail/?StoreID=Arizona-Peoria&utm_source=yelp&utm_medium=paidprofile', 'http://www.bluewaterLV.com', 'http://mrfireplace.com', None, 'https://www.redroof.com/property/az/Mesa/RRI317', None, 'https://www.phoenixyouththeatre.com', 'http://highlifesmokes.net', 'https://www.mattressfirm.com/stores/oh/macedonia/mattress-stores-macedonia-oh-44056-7165.html', 'http://www.orangeolivenoda.com', '1592348863', 'https://www.carrabbas.com/locations/az/gilbert?utm_source=yelp&medium=social&utm_campaign=location_listings', None, 'http://www.hawkerbar.com', 'https://www.estrellaent.com', 'http://www.torontodonvalleyhotel.com/en/dining/restaurants-bars', None, 'https://maps.rbcroyalbank.com/locator/searchResults.php?t=6702', 'https://www.uber.com/fr-CA/', 'http://salvatorestomatopies.com/', 'https://autoglassnow.com/charlotte-ya/', None, 'https://www.walmart.com/store/387/chandler-ok/whats-new', 'http://www.ziarecords.com/', 'https://www.robinsplumbing.com', 'https://www.harveys.ca', 'http://www.superpumper.com', 'http://easternblocvapes.com/', 'http://www.mintmuseum.org', None, 'http://www.copperwestroofing.com', 'http://www.starbucks.com/store/7493/', None, None, None, None, None, 'http://www.target.com/', None, 'http://ProTechServiceMan.com', 'https://www.squeegeebroswindowcleaning.com', 'https://eecpa.com', 'http://vapevaultinc.com', None, 'http://www.roses-spa.ca', 'http://www.papagoinnscottsdale.com', None, 'http://www.autotrend.net/', '1592348944', 'http://www.nicosbarbershop.com', 'http://www.americasbestvalueinn.com/bestv.cfm?idp=30013', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.lasvegassouthwesttoursinc.com', None, 'https://saludcerveceria.com', 'https://locations.postnet.com/az/scottsdale/10869-n-scottsdale-rd', 'http://www.drdavidhecht.com', 'http://www.kokosbakery.com', 'http://chitchatplaycafe.com/', None, 'http://chefstef4.wixsite.com/fanniecakesbakery', 'http://rocksolidhomerepair.com', 'https://wigwamarizona.com?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, None, 'http://www.antiquiteapittsburgh.com', 'http://www.kollingerautobody.com/', 'http://www.dettorespizza.com', None, 'http://www.rhapsodielle.com', '1592348994', 'https://innovativeplumbingpros.com/plumber-las-vegas/', 'http://www.ohmydogboutique.com/', 'http://www.phxbariatric.com/', 'http://www.dominos.com', 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://simplymarvelloussalonandspa.com', None, 'https://www.starbucks.com/store-locator/store/68201', None, 'http://www.concordflowershops.com', 'https://www.rona.ca/fr/Rona-h-dagenais-fils-inc-saint-sauveur-saint-sauveur', 'http://www.carnevalegallery.com', 'http://www.mycomputerwiz.net', None, 'http://www.thedirtybird.ca', None, 'https://elevatedlasvegas.com', '1592349036', 'http://cthomeaudio.com/index.html', 'http://www.globesalon.com', 'https://www.familydollar.com/locations/az/phoenix/26308', None, None, '1592349050', 'http://www.edsrealscoop.com', 'http://velocityaz.com', None, None, None, 'http://cupandcut.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.airstreamofscottsdale.com', None, 'http://wonderfulfootspa.business.site', None, None, None, 'http://crawlvegas.com/', 'https://www.bobevans.com', 'http://www.northstapleydentalcare.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, None, 'http://www.ridgepointapts.com', None, 'http://www.HoganImaging.com', 'http://commercialseatingspecialist.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=12236&localechange=1', 'http://www.susiesmamabear.com', 'http://www.gateswildlifecontrol.com', None, None, 'https://www.jewelertempe.com', 'http://www.assurednotaryservices.com', None, 'https://puls.com/phone-repair-phoenix', None, None, 'https://local.fedex.com/nv/las-vegas/LASA/?cmp=LOC-1001545-3-2-971-1110000-US-US-EN-YEXTLISTFEDEXSC', 'http://www.dynastyautogroup.com', None, 'http://www.blindoccasions.com', '1592349135', None, 'http://www.qvisionaz.com/', None, 'http://www.starbucks.com/store/11752/', 'http://www.crossfitrecursive.com', 'http://www.gratefulheadsalon.ca/', None, 'http://www.cietaylor.com?cmpid=B9T7_BLM_0006', 'http://www.tpl.ca', 'https://anticachampaign.com', None, 'https://digitalmarketinggilbertaz.com', 'http://zafrankababpalace.com', 'http://www.barneys.com/store/R-store-255', None, 'http://www.bulwarkpestcontrol.com/mesapestcontrol.php', 'http://www.smilearizonadentistry.com/', 'https://mylocalmcds.com/willow-pass-concord', None, 'http://holisticbodyoptions.com/', 'http://google.com', 'http://www.drinkatthedrink.com', 'http://www.stonelikerefinishing.com/', 'https://www.discounttire.com/store/nc/monroe/s/1620?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', None, 'http://www.dunkindonuts.com', 'http://www.LasVegasPianoSchool.com', 'https://www.redlobster.com/locations/list/nc/matthews/9801-independence-pointe-pkwy', 'http://sweetbubblesoap.com', '1592349202', 'http://www.cooperclimatecontrol.com', None, 'https://www.lasvegasgc.com', None, 'http://sogen.ca', None, 'http://www.stlawrencecoinlaundry.com', 'http://www.thegoldsmiths.ca', 'http://www.autarchicspecshop.com', 'http://www.montysblueplatediner.com/', 'https://www.choicehotels.com/pennsylvania/pittsburgh/quality-inn-hotels/pa780/rates', 'http://Tattoosocialclub.weebly.com', 'https://www.tvcarizona.com', None, 'http://www.fastneedle.com', 'http://paladinalandscaping.com/', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', None, None, 'http://www.cmlibrary.org/locations/branches.asp?id=15', 'http://www.thegreathall.ca', 'http://www.metro-arts.org/', 'http://www.moonchiro.com', 'http://www.robertsoncosmeticcenter.com', None, None, 'http://www.drfarian.com', 'http://www.lbmbar.com', 'https://www.mondou.com/en-CA/store-listing/s-mondou-lasalle/2008', None, 'https://www.capriottis.com', 'http://www.desertcuts.com/east-phoenix/', None, 'https://www.mattressfirm.com/stores/az/chandler/mattress-stores-chandler-az-85286-8086.html', 'http://www.aerialclt.com', '1592349278', '1592349281', None, 'http://www.usflatratemovers.com/', 'http://www.nandos.ca/restaurants/bay-street', 'http://www.triplebgaragedoors.com', 'https://drafthouse.com/phoenix/theater/gilbert?utm_campaign=yelp-page&utm_content=businessurl&utm_medium=social&utm_source=yelp.com&utm_term=gilbert', 'https://www.intownsuites.com/extended-stay-locations/arizona/gilbert/east/', 'https://www.wellsfargo.com', 'https://www.velofix.com/locations/east-valley/', 'http://www.STLBridalSweets.com', None, None, 'https://www.pteglv.com/locations/pts-gold/ann-camino-al-norte/', 'http://jackbeagles.com/', 'http://www.pittsburghdancecenter.com', 'http://www.carpetkingdomaz.com', 'http://dufferinpark.ca', 'http://www.LLMirrorGlass.com', 'https://www.planetfitness.com/gyms/gilbert-greenfield-lakes-az?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://houlihans.com/', None, 'http://www.torontolaserservices.com', None, 'http://locations.michaels.com/on/mississauga/3952/index.html', None, 'http://www.timhortons.com/ca/en', 'http://www.letusgetdirtyforyou.com/', 'http://www.gethiredpro.com', None, None, None, None, 'http://www.Budgetfencecompany.com', None, None, 'http://www.foxandfiddle.com', 'http://www.generationspractice.com', 'http://www.newbambooasiancuisine.com', 'http://www.charlottekoa.com', None, 'http://www.boardandbrush.com/ahwatukee', 'http://www.peaceofedensalon.com', 'http://www.avondalegaragedoors.com', None, None, 'http://bibibop.com', 'http://www.mteverestrestaurant.ca', 'https://www.sprouts.com/stores/details/-/store-details/view/store/20/?utm_source=yelp&utm_medium=listing&utm_campaign=website', None, 'http://www.drainsquadplumbing.com/', 'https://deannasanders.glossgenius.com', None, 'https://www.amazinglashstudio.com/studios/az/glendale/arrowhead', 'http://www.tremontanimalclinic.com', None, 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', None, None, 'https://stores.mooresclothing.com/ab/calgary/415---3545-32nd-ave--ne.html?utm_source=yelp&utm_medium=listing&utm_content=41&utm_campaign=AB', None, None, 'http://www.oldalleghenyshoppe.com', 'http://balesbestplumbing.com', 'http://www.mcorealty.com', 'http://www.fishcreeknissan.com', 'http://www.narai-restaurant.com/', 'http://www.dbsservicecenter.com', 'https://www.verdipizza.com', '1592349432', 'https://www.pizzahut.ca/store-details/store-R31407/pizza-hut-Scarborough', 'http://azflyerservice.com/', 'http://www.giantgenie.com', None, None, 'https://www.alejaygreencleaning.com', 'http://www.qhautecuisine.com/', 'http://comairservice.com/', 'http://www.thegoodwich.com', 'https://www.warbyparker.com/retail/toronto/684-queen-st-w', 'https://beres-mexican-food1.business.site', 'http://www.angiespizza1.com', 'https://www.purr-fectpetsitting.net', None, None, None, 'https://www.9round.com/fitness/charlotte-nc-x4589', 'http://gcuhotel.com/restaurant/', 'http://www.revolutiondanceandarts.com/', 'http://www.dentist-tempe.com', 'http://www.kylemontoyatattoos.com', 'http://www.myprinciplefitness.com', None, 'https://desertbirkenstock.com', 'http://pelicanssnoballs.com', 'http://mobilecardr.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700007898397760&ds_s_kwgid=58700000649767852&ds_e_adid=%7Bcreative%7D&ds_url_v=2&cmpid=ADV_PG_%5B*KeywordID*%5D', '1592349497', 'http://redlinelv.com/', 'https://littlehutcafe.com', None, None, 'https://www.walgreens.com/locator/walgreens-2531+cuthbertson+rd-waxhaw-nc-28173/id=11251', None, 'http://www.leenasfoodtruck.com', 'http://www.nolimitsdanceandfitness.com', 'http://unatakeaway.com', 'http://www.indiantrailcdjr.com/index.htm', 'http://www.ControlledComfortlv.com', 'http://www.mycrowandowl.com', 'http://www.parksideaptsaz.com', None, 'https://hashkitchen.com', 'http://www.glamourbeautybarlkn.com', 'https://www.enercare.ca/locations/caledon-orangeville', 'http://www.carolinahomeseller.com', 'http://electronicsquare.ca', 'http://comidahudson.com', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', None, 'http://www.deltaco.com', None, None, 'https://www.mirandadelivery.com', 'http://www.tbonesonthelake.com', 'https://zbodsspraytanning.com/north-scottsdale', 'https://www.bridlewoodeyecare.com', 'http://www.cyclonelasvegas.com', 'http://www.pieceofcakeaz.com/', 'http://www.OpinionEx.com', 'http://www.thecaptainsboil.com?utm_source=Yelp&utm_medium=Click&utm_campaign=AB_1324D&utm_content=mainlink', 'http://www.kayabeautysalon.com', '1592349590', None, 'https://www.southstburger.com/location/st-clair-rushton/', None, 'http://terrazzato.com', 'http://www.dominos.com', None, 'http://www.westvalleyperio.com', 'http://www.prettysmartguys.com/', 'https://cocofreshtea.ca', None, None, None, 'https://sebastians-rolling-chicken-llc.business.site', 'http://destinationspasalon.com/Salons/Manhattan/index.htm', None, '1592349623', None, 'http://www.greenbeanery.ca', None, None, 'http://www.globalpetfoodstoronto.ca/locations/beaches/', None, 'https://www.wyndhamhotels.com/hotel/06944?tel=18003291073&iata=00093785&cid=fe:di:20161220:yl:pp:dius:06944', '1592349642', 'http://stlouiswings.com', 'http://www.mtnebopizzaroma.com', 'http://www.fur-everhomesrescue.com/', 'http://www.beachcombertruck.com', 'https://www.magnoliaicecream.com', None, 'https://www.sanmicheleapartments.com', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Phoenix-AZ-85004/721064/', 'https://www.rwcgroup.com/map-hours-directions-trucks-dealership--hours-phoenix-headquaters', 'http://vegasexoticrentals.com', 'http://namcoarcade.cf', None, 'https://zbarandgrille.ca', '1592349679', None, None, 'http://www.embassylv.com', 'https://locations.dignityhealth.org/chandler-regional-medical-center-chandler-az', None, 'https://www.gotjump.com/arizona/chandler/', 'http://www.keycmi.com', None, 'http://www.architecturalstoneelements.com', 'http://www.ldgdental.com', None, 'http://www.richmondhillveterinarian.ca', 'http://www.groutmagicianphoenix.com', 'https://www.hardees.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.urbanactive.com', 'http://theredmouse.com/', 'http://www.amazingbookspgh.com', 'http://www.arizonaretinainstitute.com', 'https://newyouspas.com', None, 'http://mundodentistry.com', 'http://mingswokxpress.com', None, 'https://www.mallardscrossingapts.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://www.goodwill.org', 'https://www.bestwestern.com/en_US/book/hotel-rooms.66121.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:66121', 'http://www.justaddwaterscuba.com', 'http://www.johnflorendo.com', 'http://www.cabowabocantina.com/vegas/', 'https://stores.loft.com/outlet/us/nv/las-vegas/7400-las-vegas-blvd-south.html', None, 'http://www.foxspizzamtwashington.com', 'http://www.wigstudioetc.com', None, None, None, 'http://www.tintcartelaz.com', None, 'http://www.icesports.com/oakville', 'http://www.toysrus.ca', 'http://www.lvcriminaldefense.com', None, 'http://www.whiskeyriversaloon.com', 'http://www.eastvalleyanimal.com/', 'https://www.wellsfargo.com', None, 'http://independentpgh.com', 'http://karireyewear.com/downtown/', 'http://www.unitedlockservice.com', 'http://www.audilasvegas.com', None, None, 'http://www.johnvarvatos.com/storedetails?StoreID=5656', 'http://www.subway.ca', None, None, 'http://www.theretreatapts.com', 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?language=EN&STORE=532', 'https://www.usps.com/', None, 'http://www.redmangousa.com', 'http://www.unitypoint.org/MeriterFoundation', None, 'http://www.jacquelinehanna.com', 'http://www.lanceburton.com/', None, 'http://www.siamlifestylespa.com', 'http://www.playtownsquare.com', 'http://www.meckabc.com', '1592349851', None, None, '1592349856', 'http://www.phoenixglow.com', None, 'http://fitchburg.orangeshoe.com/', 'http://www.trailsdynasty.com', 'http://www.desertwide.com/', 'http://sisenorwestlake.com', 'https://www.speedycash.com/find-a-store/nevada/las-vegas/flamingo-and-jones?utm_source=yelpstorelocator&utm_medium=Affiliate&utm_content=afflink', 'http://abckidseyes.com', 'https://www.walmart.com/store/5497/evans-mills-ny/whats-new', None, None, None, None, 'http://www.huntersvillencdentistry.com', 'https://www.yardhouse.com/locations/nv/las-vegas/las-vegas-town-square/8319?cmpid=br:yh_ag:ie_ch:dry_ca:YHQ121LOCURL_dt:20200609_sn:yelp_gt:las-vegas-nv-8319_pl:locurl_rd:1018', 'http://www.drrummell.com/', None, 'http://www.renewmedicalspalv.com', 'https://struckcontemporary.com', 'https://www.petsmart.com/stores/us/oh/mayfield-heights-store1465.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.sandellas.com', None, 'http://www.mccartneychiropracticsc.com', None, 'http://www.mrschnappspubandgrill.com', 'https://www.templemojo.com', 'http://www.manningfamilydentistry.com/', 'http://www.cannabiscookingcompany.ca', 'http://www.deftmovers.com', '1592349922', 'https://www.panerabread.com/en-us/home.html', 'http://www.SUMathletica.com', '1592349929', 'https://www.holyangelsnc.org', 'http://www.arizonasprinkler.com', 'https://vegasexperience.com/slotzilla-zip-line/', None, 'http://www.zellers.com', 'http://www.canadacurrencycentre.com', 'http://www.azfamilyrealty.com', 'http://www.stormcinemas.co.uk/belfast/', 'http://www.perfectthreading.com', 'http://www.slickbartender.com', 'http://www.legendsbaseball.org', 'https://www.tlc4gums.com', 'https://www.cutmenssalon.com', None, 'http://clutchcuts.com/', 'http://advantageurgentcare.com', 'https://www.entdocaz.com', None, 'http://www.baronecanada.com', None, None, 'http://torontobotanicalgarden.ca/enjoy/special-events/market2013/', None, None, 'https://store.vioc.com/oh/north-randall/4580-warrensville-center-rd-44128-060027', 'https://thomasmidtown.com', 'http://www.elte.com', None, 'http://www.thegreatestatesale.com', 'http://calibercollision.com/locate-a-caliber-collision-center/centennial-hinsdale-cir', None, 'https://www.kennyrossfordsouth.com/service.aspx', 'https://www.hilton.com/en/hotels/cmichgi-hilton-garden-inn-champaign-urbana/?SEO_id=YELP-GI-CMICHGI', 'http://www.pallensautoconcepts.com', 'https://www.touchupssalon.com', 'http://www.ellehardware.com', None, None, 'http://www.nirvanahairsalonandspa.com', None, None, 'http://www.coachsclub.com/', 'http://www.omrestaurant.ca', None, None, '1592350057', 'http://barosolutions.com', 'http://ayurzona.com', 'http://surpriseazchiro.com', 'http://www.spicekingsrestaurant.ca', 'http://www.cosmoscafe.com', 'http://www.cowboysnightclub.com', None, 'http://www.danecountyfair.com/', 'http://www.tuffspas.com', 'http://www.triusandaim.com', '1592350094', 'http://www.spirithalloween.com', 'http://papispuertoricancuisine.com', 'http://www.appliancedoctorsaz.com', None, 'https://www.focusedtattoos.com', '1592350115', 'https://locations.riteaid.com/locations/pa/irwin/328-334-main-street.html', 'http://www.ultracuts.ca', None, 'http://www.flocrit.org', 'http://www.smartypantsconsign.com', 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', 'http://www.amresprop.com', None, 'http://www.jabzboxing.com/pinnaclepeak', None, 'http://www.visiondevelopmentinstitute.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://botanicalsalonandspa.com', 'http://www.crockadoodle.com/unionville', '1592350166', 'http://www.boulderpalmsapartments.com/?campaign_code=yelp_Boulder_Palms_NV_89121', 'https://www.jessicanailsandspa.com', 'https://www.playtrimiddleton.com', 'http://www.banfield.com/veterinarians/az/peoria/lkp?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.wefixuglyplumbing.co', 'http://www.midwoodpetsitting.com', 'https://www.hamarusushi.com', 'https://www.acerentacar.com/landing/lp_clto01.aspx', None, 'http://www.metrosotherwoman.com/charlotte-location', 'http://www.lululemon.com', 'https://www.purebarre.com/location/rocky-river-oh', 'http://www.thecleaningauthority.ca/mississauga/', None, 'https://difrancocontractorsinc.com', 'http://www.mrtortas.com', 'https://cocofreshtea.ca', 'http://jakesbistro.ca', 'https://locations.wendys.com/united-states/oh/oakwood-village/23050-broadway', 'http://www.inthedogzhouse.com', 'http://www.prismeyeinstitute.com', 'http://www.adobeanimalhospital.com/homepage.pml', None, None, 'https://www.newyorknewyork.com/en/nightlife/the-chocolate-bar.html', None, 'http://www.sunsetclinic.us', 'https://www.hermanheylflorist.com', None, None, None, 'https://zappoelectric.com', 'https://claymoreimports.com', None, None, 'http://www.anthemdental.com', None, None, None, 'http://www.etpittsburgh.com', 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', 'http://hiltongardeninn3.hilton.com/en/hotels/ohio/hilton-garden-inn-cleveland-downtown-CLEGWGI/index.html?SEO_id=YELP-GI-CLEGWGI', 'http://www.finelinecustomworks.com', None, 'https://abrazomedicalgroup.com/amg-north-scottsdale/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://desertbreezeyoga.com', None, 'http://www.pomo2go.com', 'http://www.tibertifence.com', None, 'https://locator.chase.com/nv/las-vegas/6460-sky-pointe-dr', None, 'http://tempechiro.net', 'http://www.studio3arts.com/', 'http://www.thetravelingphotobooth.com', '1592350361', 'http://breakthroughperformance-rehab.com', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'http://www.ubreakifix.com/locations/eastmadison/', 'https://www.walgreens.com/locator/walgreens-16711+birkdale+commons+pkwy-huntersville-nc-28078/id=7400', None, 'http://www.bananarepublic.com', 'http://patisserieroyale.com', 'https://www.amctheatres.com/movie-theatres/charlotte/amc-classic-rock-hill-7?utm_uid=yelp', 'http://www.richmondspub.com', 'http://www.scottsdaleplaza.com', 'http://Evelialupianphotography.zenfolio.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.ahalocksmith.com', 'https://www.chocolatsfavoris.com/en', None, None, 'https://realdemichoacan.business.site', 'http://www.thesmilecreators.com', 'http://www.llgi.org/champaign', 'http://www.les5saisons.ca', 'http://www.amgnevada.com', 'http://www.themainstreetgroup.net', 'https://www.scottybeans.com', None, 'http://www.redrobin.com/', None, 'http://www.urbanvinephx.com/', None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, '1592350481', 'http://www.ops602.com/about-2/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://yinzburghbbq.com/', 'http://www.rivierahotel.com/las-vegas-entertainment/crazy-girls.aspx', None, 'http://www.tacotime.com/', 'http://www.townestorage.com/self_storage/Las_Vegas_NV/zip_89113/towne_storage/1379', 'https://www.batteriesplus.com/store-locator/nv/lasvegas/batteries-plus-327?utm_source=yelp&utm_medium=local&storecode=327', None, None, None, 'http://www.yankeecandle.com', 'http://adioaz.com', None, 'http://ifixmobilesaz.com', 'http://christies-alterations.com/', None, 'https://www.mosaicsouthend.com', 'https://thestockshop.org', 'http://www.ihg.com/staybridge/hotels/us/en/charlotte/cltcc/hoteldetail', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.boubahspetstore.com/', 'http://www.bubbleleecanada.com', 'http://www.pota-oakland.com', 'http://www.bajafresh.com/stores/30407', None, None, None, None, 'http://www.mcclintockfamilydental.com', 'https://www.barefootsurfaces.com', 'http://www.tbynum.com', 'http://www.brewersconnection.com/', None, '1592350601', 'http://www.arizonamobilityscooters.com', 'http://www.discount-drugmart.com', '1592350612', '1592350616', 'https://www.thesterlinggilbert.com', 'https://www.caseyolsondesigns.com', None, 'http://www.sestilinursery.net', None, 'https://www.barlouie.com/locations/us/oh/westlake/crocker-park?utm_source=other&utm_medium=listings', None, 'http://www.timhortons.com', 'http://www.dixiescharlotte.com', None, None, 'http://tabule.ca', '1592350654', None, None, None, 'https://pink-file-nails.business.site', 'http://www.myfitnessstudioaz.com', None, 'http://www.butterflywonderland.com/', 'https://locations.monro.com/pa/north-versailles/1813-lincoln-highway?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', 'http://www.groovypetgrooming.com', 'http://www.kathynailsspa.ca/locations.html', 'http://www.centrotrattoria.com', None, 'http://www.norskgolfclub.com', 'https://heckerrealestate.managebuilding.com/Resident/Public/Rentals?location=89113', 'http://www.danalaurensalon.com', None, 'https://www.ulta.com/stores/monroeville-pa-169', 'http://www.sundevilgaragedoorsaz.com/', '1592350713', 'https://www.flexgym.ca', None, 'https://www.lindt.ca/en/stores/lindt-chocolate-outlet-halton-hills-premium-outlet', None, None, 'http://hotelcaliforniarestaurant.com', None, 'https://www.homeownersig.com', None, 'https://www.dillards.com/stores/southpark-center-strongsville-ohio/0364', 'http://www.lastdefencelounge.ca/', 'https://www.urbanbarn.com/en/stores-detail/?id=C513', 'https://www.skyviewmotors.com', 'https://www.intact.ca', 'https://www.t-mobile.com/store-locator/az/gilbert/e-warner-rd-s-val-vista-dr?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://houseoftennis.shop', 'https://www.wellness1stimc.com', '1592350760', None, None, None, None, 'http://www.behomes.com', 'http://arrowheadpt.com', 'https://www.healthinsideout.com', 'http://emilianos.net', 'http://www.sipandsavortours.com', 'http://www.burlingtoncoatfactory.com/store-details-Store-213--5959-West-Sahara-Avenue--Las-Vegas--NV--89146-3126.aspx?id=2d282a9a-6b10-4437-bb42-7194af655b83&from=89146', 'http://www.graniteluxuries.com/', None, 'https://www.urbanbarn.com/en/stores-detail/?id=C203', 'https://www.walmart.com/store/5186/gilbert-az/whats-new', 'http://kaizenautocare.com/body-shop-gilbert-az/', 'http://azallstarclean.com', 'http://www.hyundaiofbedford.com', 'http://www.mickefynns.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.momotruck.com', None, 'https://www.bagsandragsaz.com', None, 'http://www.kellyhawkins.com', 'http://westpointmarket.com', 'http://www.kendallplumbingandrooter.com', 'http://www.winerack.com', 'http://www.coffeebean.com', 'http://www.hellodoggygrooming.com', 'http://www.myimagemart.com', None, None, 'http://www.eatiriepatties.com', 'https://bostonpizza.com/en', 'http://www.resonance-wellness.com', 'http://www.midas.com/toronto/store.aspx?shopnum=9583&dmanum=857001', 'http://www.crystalsmirrorimage.com', 'http://www.wolfsonmedicalcenter.com', None, 'http://littlevillagegrillcharlotte.planetcafepages.site', None, None, None, None, 'http://pawsitivelypamperedpets.com', 'http://www.priape.com', 'http://www.affinitycarrentals.com', None, 'https://www.jiffylube.com/locations/AZ/Gilbert/2084', 'http://www.cbac.com/gilbert-santan', None, 'http://www.apostrophelounge.com/', None, 'http://ecofriendgreen.com', None, None, 'http://www.sbarro.com/', None, 'http://www.pitajoint.com', None, 'http://www.azcossurg.com/', 'http://www.thebohemiangastropub.com', None, None, 'https://www.classicgoldauto.com', 'http://www.eastoverfootandankle.com', 'https://mourelatos.com', 'http://www.lifestyle-pilates.com', 'http://www.vanguardcleaning.com/locations/nv-las-vegas-cleaning-services', 'https://www.thewavebarandlounge.com', None, 'https://www.mamalandresto.com', '1592351012', None, 'http://www.alfsantiques.com', '1592351019', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.inglewooddrivein.com/', 'http://www.godental.ca', 'http://elginfurniture.com', 'http://www.caesarspalace.com/casinos/caesars-palace/hotel-casino/property-home.shtml?source=PSx5x72166&creativeproperty=CLV&site=google&adg=Branded_LV&kw=ceasars_palace_las_vegas&act=LAV&cmp=LAV_CLVOcc.Top-Phrase', 'http://www.hamptonsgolfclub.com', 'https://saltcavevaughan.ca', 'https://spectrumretirement.com/mountainpark-senior-living-az-phoenix/?utm_source=Yelp', 'http://www.aseparaterealityrecords.com', 'http://cuthairstudio.com/', 'https://shady-airbrush-tanning.business.site', 'http://www.cardiacsolutions.net', None, 'http://chinabuffetcharlotte.onlunchroom.space', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.cleaningservicephoenix.com', None, 'http://azarthritis.com', None, 'http://www.silsauto.com', '1592404416', 'http://www.treasures-by-tina.com', 'http://mapleleaftavern.ca', None, 'http://www.bistrochezanne.ca', 'http://www.papasammyspizza.com', 'http://www.arbys.com/', 'http://www.twistedimage.net/', 'http://www.houlihans.com/my-houlihans/pittsburgh-station-square?utm_source=yelp&utm_medium=organic', 'http://www.healingtouchcharlotte.com/', 'http://www.voicepluscommunications.com', 'https://weldins.business.site', 'https://centralselfstorage.com/storage-units/az/glendale/5240-w-cactus-rd/', None, 'https://www.capricamelback.com', 'http://www.starbucks.com', None, None, 'http://www.halesmarineservices.com', None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'https://agents.allstate.com', 'https://www.choicehotels.com/north-carolina/gastonia/comfort-suites-hotels/nc028/rates', 'http://www.hausertree.com', '1592404510', 'http://www.buddiesinbadtimes.com', 'http://www.stopnshopfood.com', 'http://www.julescafe.ca/', 'http://www.LightSportAviationLLC.com', None, 'http://www.venturescarrentals.com', 'http://www.toronto.ca/parks/parks_gardens/humberbay2.htm', None, 'http://www.monkeyedge.com', 'http://rotipalaceofindia.ca', 'https://www.caesars.com/flamingo-las-vegas/shows?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=BugysCabaret&utm_content=Entertainment', None, 'http://www.luckysburgers.com', 'http://www.mintthaicafe.net', 'http://www.thecruxclimbing.com', 'https://bywoops.com/southpark/', None, 'http://rodspaintinglv.com', 'http://www.kerabath.com', 'http://www.chrisanthonyfitness.com', None, 'http://www.mysafehaven.com', 'http://www.wholesalecabinetcenter.com', '1592404598', 'http://www.grandepizzaitalianrestaurant.com', None, 'http://www.hasslefreeclinic.org', 'http://firestormpizza.com', 'https://order.qdoba.com', 'https://stores.petco.com/oh/mentor/pet-supplies-mentor-oh-1948.html?cm_mmc=YELP-_-OH-_-Mentor-_-1948', 'http://www.klarenfeldgermanshepherds.com', 'https://www.mattressfirm.com/stores/az/tempe/mattress-stores-tempe-az-85282-6943.html', 'http://www.trophyden.com', 'http://www.bathurstdupont.com', 'http://www.essentialtherapync.com', 'http://www.sissonsflowers.com', 'http://www.hydratemedical.com', 'http://www.beausgrille.com', 'https://www.aamcolv-rainbowblvd.com', 'https://www.granitetransformations.com//stores/granite-transformations-of-las-vegas/?utm_campaign=2018&utm_source=Yelp', 'https://youngandpolite.com', 'http://www.sundropsnailspot.com', None, 'http://www.blumenthalcenter.org/default.asp?blumenthal=135&urlkeyword=theater_detail&objId=8', None, 'http://www.commanderspalace.com', None, 'http://Mhfitnesstraining.com', 'http://www.7-eleven.com/?yelp=36154', None, None, 'http://www.simpsonpropertygroup.com/apartments/chandler-arizona/coronado-crossing-chandler?vrurl=yelp.com', None, 'http://www.villagepoolsandspas.com', 'http://www.futureforwardwellness.com', None, 'https://milios.com', 'http://www.livinglightingrichmondhill.com', None, 'http://www.albertacarpetcleaningcalgary.ca', 'http://www.arthaircolorstudio.com/', None, 'https://www.bbvacompass.com/USA/AZ/Gilbert/630-S-Gilbert-RD/', 'http://www.torchcigarbar.com', 'http://www.casadeshenandoah.com', None, 'http://www.RescueCarpetCleaning.com', None, 'http://www.justforpleasurenc.com/just-for-pleasure-2-north-charlotte-nc/', None, 'http://www.lindahamiltonphoto.com', None, None, 'https://www.autozone.com/locations/nv/north-las-vegas/395-w-centennial-pkwy.html', None, None, 'http://www.bojangles.com', None, 'http://www.bikeshop-lv.com', None, None, None, 'http://www.upmc.com/services/urgent-care/locations/pages/wexford.aspx?curloc=&daddr=40.62302,-80.053028', 'https://www.homedoctorpest.com', 'http://www.frysfood.com', 'https://www.the-real-kk.com', None, '1592404815', 'http://www.teambangs.com', 'https://locations.wendys.com/united-states/nc/cornelius/20410--w-catawba-ave', 'http://www.eatatlatitude41n.com', 'http://www.atomicguitarworks.com', 'https://www.bjs.com/cl/middleburg-heights/0124', 'http://www.7-eleven.com/?yelp=29384', 'http://www.bobbyfresh.com', None, None, 'http://www.appleautoglass.com/windshield-repair-replace/ON/Pickering.aspx', None, 'http://www.agentsteele.com?cmpid=wc9n_blm_0006', None, None, 'http://allurebeautycle.com', None, 'https://locator.chase.com/nv/las-vegas/6460-sky-pointe-dr?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.shawnessyregistry.com/', None, 'http://www.ballantynepedo.com', 'https://www.redlobster.ca/locations/list/ab/calgary/100-6100-macleod-trail-sw', 'https://www.batteriesplus.com/store-locator/wi/madisonwest/batteries-plus-571?utm_source=yelp&utm_medium=local&storecode=571', 'http://www.pennauto.us', 'http://www.auntieannes.com/', 'https://www.littleburgundyshoes.com', 'http://www.mattressfirm.com', 'http://www.skinoasisspa.com', None, 'https://www.maaco.com/locations/nc/charlotte-11619/', None, 'https://www.onqpm.com', '1592404889', None, 'http://Joemaxxcoffee.com', 'http://mecklenburgcountymarket.com/', None, 'https://www.dynamiteclothing.com/ca/locator/ca/ab/calgary/168-Chinook-Centre', 'http://www.PondGnome.com', 'http://floorcoveringmills.com/', None, 'http://www.theaterx.com', None, 'http://specialtypainmanagement.com', None, 'http://www.mannysair.com/', 'https://www.24hourfitness.com/gyms/henderson-nv/green-valley-active', 'http://www.spirithalloween.com/store/Alma-Elliot-Square/16474139.uts', 'http://www.arbys.com', 'http://www.0109dessertnchocolate.com/', 'http://www.econrads.com', None, 'http://www.u-swirlarizona.com', 'http://www.bp.com/en_us/bp-us', 'https://www.goodnightpeds.com/locations/phoenix-az/south-mountain', '1592404940', None, 'http://barracudapoolservice.com', 'http://www.sonicdrivein.com/', 'http://www.robsquality.com', 'http://www.monkeesofcharlotte.com', 'https://perry.zeppes.com', None, 'http://www.erinmillsfitness.ca', 'http://mastakos.com', 'http://www.customxray.com', 'http://www.treats.com/', 'https://www.sundevilliquidation.com', 'https://www.usps.com/', 'http://pendelispizzalaval.com', 'https://www.sonoraquest.com/find-a-location/glendale-59th-ave-eugie/', 'http://www.madison.va.gov/', None, 'http://www.acehardware.com/store-details/11311', 'http://www.humbercinemas.com', None, 'http://www.britishspeedshop.com', None, 'http://www.gamblersgeneralstore.com/', 'http://www.eyecarecenter.com/locations/index.html', 'https://locations.captainds.com/ll/US/NC/Charlotte/2838-Freedom-Dr', None, None, None, 'https://www.kfc.ca//store/415-mount-pleasant-rd-toronto', 'http://calgarybeerfest.com', 'https://www.aspendental.com/dentist/az/goodyear/15530-w-roosevelt-st-ste-e106?utm_source=yelp&utm_medium=lociqyext&utm_campaign=Goodyear%2CAZ%7C%7CGoodyer_AZ%7C%7C8490&utm_content=listing', 'http://www.mongacanada.com', 'https://www.whiplasheslv.com', '1592405018', 'http://www.iqcando.com', None, 'http://www.instant-recall.com', 'https://www.homedepot.com/l/N-Las-Vegas/NV/North-Las-Vegas/89032/3307?cm_mmc=seo-yelp&', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sanantoniofishmarket.com', None, 'http://www.starbucks.com/store/9334/', 'http://www.littlecaesars.com', 'http://the-sun-club.com', 'http://www.ontarioqualitymotors.com', 'http://www.westriverfloral.com/', None, None, None, 'http://www.cafecocoaboulangerie.ca', 'http://www.sweetsfromheaven.com', 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://www.mississauga.ca/portal/discover/parksandgardens?paf_gear_id=9700018&itemId=200028', 'http://www.fisherscafe.com', 'http://newchinacuisine.com', 'http://shopdap.com', 'http://www.zeroturnhq.com', 'http://drmarouk.com', None, 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.kneaders.com', None, 'https://www.wildfiresteakhouse.com', 'http://pulmonaryassociates.com', 'http://www.bennettsautorepair.com', 'http://www.soma.com/store/home.jsp?cmp=MOC_yelp', None, 'http://www.purcelltire.com', 'http://www.closetmasters.net', 'http://www.pvkarate.com', 'https://www.circlek.com/store-locator/us/avondale/3-e-main-st/2700822', 'http://www.azcosmeticdds.com/', 'https://www.sheridancollege.ca', 'http://www.winebutler.ca/', 'http://www.pumpernickels.ca', None, None, 'https://www.hallofframes.com', 'https://www.haircutmensteelecreeknc.com', 'http://www.mckenzieta.ca', 'https://www.crittercontrol.com/office-finder/ontario/toronto?utm_source=yelp&utm_medium=cpc&utm_campaign=yelp', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.carefreeconnectionsaz.com', 'https://dweinc.us', 'https://www.newacunit.com', 'http://www.starbucks.com/store/15757/', 'http://www.guhsdaz.org', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3034+West+Lincoln+Avenue-Peoria-IL-61604/storeid=7798?cid=ps_ylp_2020', 'http://www.thekennedy.com', 'http://www.myoreckstore.com/?utm_campaign=yelp&utm_source=yelp&utm_medium=yelp', 'http://www.stnaildesign.com/', None, None, None, 'http://www.substationii.com', 'http://phoenixbbqandgrillingschool.com', '1592405157', 'https://ad.doubleclick.net/ddm/clk/434187075;236814625;l', None, 'http://icarexperience.ca', 'http://www.ciaocerino.com', None, None, 'http://www.ReverseAgingNaturally.com', 'http://www.carolinaagemanagement.com', '1592405188', 'https://stores.jcpenney.com/nc/matthews/clothing-stores-matthews-nc-0201.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-0201', 'https://fullhousedesserts.ca', None, 'http://www.celestinrestaurant.ca', 'http://bellissimobeautyacademy.com', None, 'http://www.daulatmedicalcenter.com', 'http://www.orchidsgardenrestaurant.com/', None, 'http://www.foskoskies.com/', 'http://www.jambopark.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216494&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://www.starbucks.ca', 'https://ad.doubleclick.net/ddm/clk/434429572;236814625;m', None, 'http://www.staticaz.com', None, 'https://nationwidevision.com/locations', 'http://maelaw.net', 'http://www.dunhamssports.com/stores/sporting-goods-west-mifflin-pa/', 'https://www.thedenlasvegas.com', None, 'http://www.smithbilthats.com', 'http://www.lawnmartinc.com', None, None, None, '1592405284', None, None, 'http://www.longbranchanimalclinic.com', 'http://www.goodfellaslasvegas.com', 'https://appliancerepairservicelasvegas.net', '1592405304', '1592405306', 'http://www.billhowey.com', None, 'https://local.safeway.com/safeway/az/chandler/1159-w-chandler-blvd.html', 'http://neighborhoodgaragedoor.com', 'http://www.marriott.com/hotels/travel/cltup-courtyard-charlotte-city-center/', '1592405325', None, 'http://www.dzpaintinc.com', None, 'http://barkbusters.com/', 'http://www.chucksautocenter.net', 'http://www.redlinewatersports.com', 'http://www.standardparking.com', 'http://www.ccculv.org', '1592405354', 'http://www.raysplacekent.com/', 'http://www.ataste.net', None, 'http://www.firstchoicelv.com', 'https://www.frysfood.com/storeHours?store=66000113', 'https://a1archsalon.com', 'http://7eleven.ca/store-locator/33259', 'http://www.ctcharlotte.org/', None, 'https://www.pestcontrolanteater.com', '1592405395', 'http://www.lonestarsteakhouse.com/', None, 'http://www.linkpoolscapes.com', 'http://www.cabinetstogo.com', '1592405409', 'http://www.authentictkd.ca', None, 'http://www.villafreshitaliankitchen.com', 'http://www.itsmyparty.com', None, 'http://www.academyofscuba.com', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://www.reliable-mechanical.com', None, 'http://koolsvilletattoolv.com', 'http://www.parkwaycarwash.com', 'http://www.lavillaestatesapartments.com', 'http://www.classicgrooming.com', None, 'http://arizonaroomstore.com', 'http://www.heymeatball.com/', 'http://www.vault-interiors.com/', None, None, 'http://qcah.co', None, 'https://biscaynebay.mgproperties.com', 'https://metropolitanautobody.com', 'https://www.cb2.com/stores/scottsdale-quarter/str71', 'http://www.sallybeauty.com', 'http://www.tagliosalon.com', 'http://www.azhandwrist.com', 'https://locations.theupsstore.com/nc/charlotte/2820-selwyn-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.arizonalegalmal.com', 'https://vanstirepros.com/tires-auto-repair-north-ridgeville-oh', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.freshcityfarms.com', None, 'http://www.citylightsartgallery.com', 'http://www.theperfectsetting.ca', None, 'https://www.benjerry.com/miraclemile', '1592405557', 'http://www.spcsports.com', None, None, '1592405570', 'http://www.eycweb.com/', 'https://turnerelectriccompany.business.site', None, None, '1592405584', 'http://www.bentosushi.com', 'http://clickserve.dartsearch.net/link/click?lid=43700007898397760&ds_s_kwgid=58700000649767852&ds_e_adid=%7Bcreative%7D&ds_url_v=2&cmpid=ADV_PG_%5B*KeywordID*%5D', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/calgary-3315-32nd-avenue-ne.aspx?storeid=12&code=pc', '1592405597', 'http://www.ballantynevillage.com', 'http://www.peets.com', 'http://crossfituv.ca', 'http://www.AxisPropertyAdvisors.com', 'http://www.ncbytrain.org/destinations/stations.html?id=kannapolis', None, 'http://reefdispensaries.com/locations/north-las-vegas/', 'https://babyloncut.com', 'http://www.avedainstitute.ca/index.php?/services/salon', None, 'http://www.brueggers.com', 'http://www.menchies.com/frozen-yogurt-shops/frozen-yogurt-blue-haven-qc', None, 'http://www.azdiscountgaragedoor.com', 'http://chelseatoronto.com', 'http://360communitymanagement.ca/', 'http://www.pizzerialibretto.com/', 'http://www.photographylasvegasnv.com', 'https://haircutmenmacedoniaoh.com', 'http://www.fivebelow.com', 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://www.ArizonaDesertEstates.com', None, 'http://www.earnhardtcadillac.com/', None, 'http://parexsalonceaz.com', 'http://www.andrewsformals.com', '1592405698', 'http://www.kmart.com/stores/pennsylvania/bridgeville/3141.html', None, 'http://www.dominos.com', None, 'http://www1.pharmaprix.ca/fr/store-locator/store/52', 'https://kona13coffee.wixsite.com/website', 'https://www.ysm.ca/banner_location/double-take-thrift/', 'https://vegashearing.com', 'https://www.juliecalza.com', 'http://www.santancornercafe.com', 'http://www.greatmoonbuffet.ca/', 'http://www.hillsong.com/phoenix', None, 'http://www.exige.ca', 'http://www.Phoenixhomebirth.com', 'http://www.ahn03.com/trestle/home.asp', None, None, 'https://agents.allstate.com/fontella-van-camp-glendale-az.html', None, None, 'http://www.footaction.com', 'http://www.evoswimschool.com', 'https://www.vitaminshoppe.com/sl/madison-384', None, 'http://www.choppedleaf.ca/location/deerfoot-meadows-coming-soon', '1592405791', None, 'http://www.baskinrobbins.ca', 'http://change.com', 'https://charlotteswebflorist.com', 'http://www.fitmeals4u.net', 'http://www.lcbo.ca', 'http://www.lasvegasmedicalassistant.com', '1592405819', None, 'http://www.markhameglintondental.com', None, 'http://www.rdsmithlaw.com', 'http://www.mezzanotte.ca/', 'https://www.reflectingwalls.com', 'http://www.cleopawtra.ca', None, 'http://latinenergydance.com', None, 'https://www.honolulucookie.com/?utm_source=yelp&utm_medium=social&utm_campaign=yelp_homepage&utm_content=LINQ', None, None, 'http://www.marlinmaid.com', 'http://www.goodmorningsnoresolution.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3303+South+Rural+Street-Tempe-AZ-85281/storeid=7078?cid=ps_ylp_2020', 'http://www.estrellaroofing.com/', 'http://www.jacobandsebastian.com', 'http://www.andersondrycleaning.com/tiffany-west', 'https://www.ladyjanes.com', 'http://houseofmoments.com', 'http://www.burritobandito.com/', None, None, 'http://www.lin-air.com', None, None, 'http://www.mymysterycastle.com/', None, None, 'http://www.davinails.com/', 'http://www.virtuebowling.com', 'http://www.tuesdaymorning.com', 'http://edgepark.com', 'http://bulgogibros.ca', 'https://www.lifetimefitness.com/spa/spa-salon.html?utm_source=yelp&utm_medium=directory&utm_campaign=GIL-acquisition', 'https://www.pteglv.com/locations/pts-pub/stewart-nellis/', 'http://www.benfranklinplumbingaz.com', 'http://www.cozynails.com', 'https://locations.theupsstore.com/az/scottsdale/16211-n-scottsdale-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://chandler-west.certapro.com//?source=Yelp', 'http://goodviewrestaurant.ca', None, '1592406197', 'https://www.chilis.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Charlotte-NC-28212/780070/', 'http://www.crossbonesgraphics.com', 'https://www.ilovekickboxing.com/north-las-vegas', None, None, None, 'http://www.thewrenaz.com/', 'http://www.pihma.edu', 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-del-lago?utm_source=yelp&utm_medium=local&utm_campaign=Honorhealth_Medical_Group_Del_Lago', 'http://www.uspoloassnglobal.com', None, 'https://www.dollartree.com/locations/az/glendale/4709/', None, None, None, 'https://www.thehendersonnvdentist.com', None, None, 'http://www.lifestylewindows.ca', 'http://www.busey.com', None, None, 'https://diversified-plumbing-inc.business.site', None, None, 'https://www.azezpawn.com', None, None, 'http://www.nvdocuments.com', 'http://junk-king.com/phoenix', 'https://www.lalasercenter.com/henderson/?utm_source=yelp&utm_medium=henderson&utm_campaign=henderson%20dermatology%20and%20skin%20cancer', 'http://heyjoetruck.com/Home.php', 'http://www.re-vamproofing.com', None, 'https://charlotteveteranmovers.com', 'https://www.azchimneycakes.com', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.jumpyardfun.com', None, 'http://www.pampanguena.com', 'http://www.ginospizza.ca', 'http://www.bascexpertise.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.ahdvegas.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592406358', None, 'https://www.sportchek.ca/stores/yonge-street.html', 'http://www.heroesforsalelv.com', None, 'https://angiepopa.kwrealty.com', 'http://www.burritohouseon.com', None, 'https://www.metropcs.com', None, 'http://www.idealfinecars.com', 'http://www.prestigejewelsinc.com', 'http://bcauctionhouse.com', None, 'http://www.timhortons.com', None, 'http://www.divastudio.com', None, 'http://www.blumenthalcenter.org/', 'http://www.sundancedentalcare.com', None, None, 'http://www.americanfreight.com/?utm_source=yelp&utm_medium=social&utm_campaign=profile', 'https://www.marriott.com/hotels/travel/phxaw-aloft-glendale-at-westgate', 'https://www.cvccard.com/duckyscarwash/', 'http://www.crossfitembody.com/', 'http://www.wrigleymansion.com/food-drink/', 'http://www.natures-spa.com/', 'http://www.mesamarineonline.com', 'http://www.beakst.com', None, None, '1592406472', 'http://brownesbistro.com', 'http://www.sincitycitations.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.thestandardcafe.ca', 'http://www.drah.ca', 'https://www.tobaccoleafvegas.com', 'http://www.banfield.com/veterinarians/nv/las-vegas/smm?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://www.payless.com/stores-location/NV-LAS-VEGAS-5798.html', 'https://best-friend-restaurant.com', '1592406512', 'https://www.round1usa.com/location/meadows-mall/', None, None, None, None, 'http://hideawayantiques.com/', 'http://rivermountainbikeshop.com', None, 'http://www.plowhearth.com/locations/pennsylvania/pittsburgh-pa.htm', None, 'http://www.southwestbimmers.com', None, 'http://www.dollar.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.afghankebobcuisine.com', 'http://www.walmart.ca', 'http://mmmmpizza.com', 'http://www.thebarberschairvaughanmills.com/', 'http://locations.alfredangelo.com/pa/pittsburgh/aa034/', 'http://www.bendthebridge.yoga', 'http://www.psdm-solevita.com', 'http://www.creativepoolplastering.com', 'http://west-las-vegas.windowgenie.com', 'http://parkavecatering.net/Home_.html', 'http://www.toyomotors.com', 'http://www.canyonskyent.com', None, 'http://farazauto.com/', 'https://larsengallery.com', 'http://www.quicktint.com', 'https://crandellroofing.com', 'http://www.cabinetsbycandf.com', 'http://www.pizzapatron.com', 'http://www.phoenixpubliclibrary.org/Locations/Pages/Cesar-Chavez.aspx', 'http://www.hotyogatwinsburg.com', None, 'http://www.terraproaz.com', None, 'http://www.rpirentals.com', 'https://www.evoqlv.com', 'http://www.jtiinc.com', 'https://budgetblinds.com/Strongsville/?utm_source=yelp&utm_medium=naf-listing&utm_campaign=NAF-LOCAL-YELP', 'http://www.swautoservice.ca', 'http://www.poppysplace.com', 'http://www.garagedoorrepairlasvegasnv5.com', 'http://www.apluswindowtint.net', 'http://www.sticklerspgh.com', 'http://www.lairdeglintonvet.com', 'http://www.lasvegaswedding-makeup.com/', 'http://www.sallybeauty.com/', 'http://stoneleafgroup.com', 'http://www.peachtreesouthernkitchen.com/', 'http://www.sallybeauty.com', None, 'http://7thavenuefamilyhealthcenter.org', 'https://www.styleseat.com/BellaLucehairdesign', 'http://www.naca.com', 'http://www.mcdonaldgroupcharlotte.com', None, None, 'http://www.syskoservices.com', 'http://www.nectarusa.com/', 'http://www.thefixsolutions.com/northlake-mall', 'http://www.prideconditioning.com', None, 'http://www.italiancreations.net', 'http://www.planetfitness.com/gyms/chandler-az-741?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, None, 'http://www.massagewellvegas.com', 'http://www.presidentialpools.com', None, 'https://yzagereenterprises.com', 'http://Www.luckydawgmobile.com', None, None, None, 'http://www.philippelusi.com/', None, None, 'http://www.parkette.ca', None, 'http://www.affordable-decks.com', None, None, None, 'https://www.simon.com/mall/ross-park-mall/stores/toy-land/stream/toy-land-now-open-6125942', '1592406800', None, None, 'https://tortasmanantial.com', 'https://cheddars.com/location-details/2155?cmpid=br:csk_ag:ie_ch:dry_ca:CSKQ121LOCURL_dt:20200615_sn:yelp_gt:gastonia-nc-2155_pl:locurl_rd:1131', 'http://noblepoolservices.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, 'http://bikramyogatoronto.com/', None, 'http://my.clevelandclinic.org/locations/directions/103-c-building', 'http://www.littlegreensaz.com', None, 'https://www.nothingbundtcakes.com/bakery/oh/avon-oh?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=avon-oh_269', 'http://www.sallybeauty.com/', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', None, None, None, 'http://www.yankeecandle.com', None, 'http://www.golftroop.com', 'http://www.landscapelighting.vegas', '1592406882', None, 'http://www.azreefdoctors.com', None, 'http://grind-burger.com/', 'http://cateringbymario.ca', 'http://www.yelp.com/events/charlotte-pink-social-girl-tribe-holiday-market', 'https://www.escaperoomsphx.com', None, 'http://www.reece-auto.com', None, None, 'https://carolinaseyecenterandmedspa.com', 'http://www.philsebastian.com', 'http://www.jdjonescompany.com/', 'https://samedayservice911.com', 'http://BeastPrinting.com', None, 'http://www.springbankdental.ca', 'http://Bautistalandscape.com', 'http://www.atoclimo.com', None, 'http://xoprimesteaks.com/', None, '1592406963', None, 'https://locator.chase.com/oh/madison/6572-n-ridge-rd?jp_cmp=rb/LocalListings/aff/branch/na', '1592406976', 'http://www.openwidedentalaz.com', 'http://www.truphysicaltherapy.com/', None, 'http://www.morningstarstorage.com/location/308/sc/fort-mill/carowinds/?ref=yelp', None, None, None, 'http://www.seemybabyultrasound.com', 'http://www.waldosnursery.com', None, 'http://justbounce.ca/', 'http://www.superc.ca', 'http://www.bankofamerica.com', None, 'http://www.bigfootsmokehouseandbar.com', '1592407022', 'http://www.janthonysalonspa.com/', None, 'http://www.willomedispa.com/', 'https://www.vineyardvines.com/storedetails?StoreID=127', 'http://www.freewheelbikes.org', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'http://www.surf-inn.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280223331&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.angiessalonlv.com', 'http://www.heartlandcu.org', 'https://dreells.com', None, 'http://www.sunsetcanyonapts.com', 'http://www.onearmgambler.com', 'http://www.hawkeyecustomlandscaping.com', 'http://www.mathnasium.com/northcentralphoenix', 'http://www.thecleaningauthority.com/phoenix', None, 'http://stephaniet.bhhsnv.com', None, 'http://spaandbodywork.net', 'http://www.Doctortanner.com', 'http://zikwid.com', 'https://www.westgatedestinations.com/nevada/las-vegas/westgate-las-vegas-hotel-casino/entertainment/vinnie-unfiltered', None, None, None, 'http://www.ohboyburger.com', 'http://www.feasto.ca', 'http://sunshinedental.com/', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://www.thehatrackpub.com', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2foh%2fcleveland%2fwestlake&sisearchengine=1524&siproduct=2457_Bus', 'https://capitolnorthamerican.com', 'https://dwss.nv.gov/', 'http://www.mindbodyphx.com', None, 'http://www.trilliumhealthpartners.ca/', None, 'http://locations.in-n-out.com/160', '1592407194', None, None, None, 'http://aeautomotive-az.com', 'http://www.adegarestaurante.ca', None, 'http://www.websitetigers.com/', 'http://www.squaresalon.com', 'http://www.apeainthepod.com/maternity-stores/nevada-las-vegas.asp', None, 'http://www.Donatos.com', None, None, 'http://leesatamember.com/locations/wphx/', None, 'http://www.peaceloveandlittledonuts.com/', None, None, 'http://www.ice-performance.com', '1592407259', 'https://www.myeyedr.com/locations/ballantyne?utm_source=Yelp&utm_medium=Referral&utm_campaign=ballantyne', 'http://www.cosmopolitanlasvegas.com/', '1592407268', 'http://commoncrown.ca', 'http://www.oliverbonacini.com/Malaparte.aspx', 'http://www.cmdcpa.com', 'http://KatelynDang.com', 'http://stores.sunglasshut.com/us/az/tempe/2000-e-rio-salado-pkwy.html', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.pizzanikkos.ca', 'https://aboveandbeyondpoolremodeling.com', 'https://www.dominos.com', 'http://www.cabelas.com/stores/South_Carolina/Fort_Mill/062.jsp', 'http://www.zkgrill.com', 'http://www.springmt-reflexology.com', None, 'http://www.prudentialrealty.com', 'http://www.postsurgicalrecoveryteam.com', '1592407333', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/tempe/phxte/hoteldetail', 'http://www.arizona-taxlawyer.com/', None, None, None, 'http://www.pvsmiles.com/', '1592407355', None, 'http://www.opticaleyeworks.ca', 'http://www.CarolinaBoneandJoint.com', 'https://www.cruiseshipcenters.com/Henderson', 'http://www.dixiestory-lovinghands.com', None, 'http://summerhillmarket.com/', None, 'http://www.tempehonda.com/', 'http://www.wexfordwellnesscare.com/', 'http://www.7-eleven.com/?yelp=22886', None, 'https://essmc.com', 'http://penguins.nhl.com', None, 'http://www.ptg.ca', None, 'http://www.mypizzahouse.com', None, None, 'http://www.merrymaids-centralphoenix.com', None, 'http://bluelineautogroup.com', 'https://lasvegasliving.com/properties/elevate/', 'http://www.mrmroofingllc.com', None, None, None, 'http://www.just-eat.ca/restaurants-gateway-of-india', 'http://www.longjohnsilvers.com/', None, 'http://www.cfra.vegas', None, 'http://familypracticewexford.com/', 'http://www.arbys.com/', 'http://www.cenphobb.com', 'http://www.tiptopbarbershop.ca', 'http://www.totalbody3d.com', None, 'http://www.frindellagency.com?cmpid=ll6e_blm_0006', 'https://www.usaa.com', 'http://oihnv.com', 'http://www.7-eleven.com/?yelp=29384', None, 'http://qdoba.com', 'http://www.blueadobegrille.com/', 'http://www.aurorainnohio.com/six-horses-tavern.htm', 'https://www.theshinybean.com', 'https://www.idealimage.com/medspa-locations/wisconsin/madison-area/madisonmiddleton', None, 'https://www.kfc.ca//store/415-mount-pleasant-rd-toronto', 'https://www.circlek.com/store-locator/us/henderson/3113-hwy-41-n/m0095', 'http://www.quesadillamexicanrestaurant.com/', 'http://www.masterpizza.com', 'https://www.eatnpark.com', 'http://www.rooseveltbarbershop.com/', 'http://Augustyniakteam.com', 'http://www.neonopolislv.com/', None, None, 'http://www.elginfurniture.com/locations.html?store=3', None, 'http://mygaragedoorrepairphoenix.com', None, None, None, 'https://www.choicehotels.com/arizona/peoria/comfort-suites-hotels/az125/rates', 'http://www.procare-chiro.co', 'http://www.pearlymaes.com', None, None, 'http://www.studioadt.com/', None, 'http://www.madhattermufflerandbrakes.com', 'https://www.southmountainwindowcleaning.com', 'http://www.paintedmountaingolf.com', 'http://www.pizzapalermo.com', None, 'http://mentorfamilyrestaurant.com/', 'http://smogbusters.com', 'http://www.shala-mar.com/', 'http://qualitynailstempe.com', 'http://www.gamestop.com', 'http://www.hoopstohomes.com', 'https://www.visionsource-excelvision.com', 'http://castroslounge.com', None, 'http://charlottewindowtinting.com/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.t-mobile.com/store-locator/nc/matthews/fincher-farm-potter?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://tandoorexpress.ca', None, None, 'https://www.castorage.com/self-storage-locations/arizona/goodyear-az-storage-units/2121-S-Litchfield-Road', None, 'https://www.ubreakifix.com/ca/fr/locations/dollard?srccode=yelp_track', 'https://www.asics.com/us/en-us/store/AAC-5718?lat=36.1634205&long=-115.1588431', None, 'http://www.snbmotors.com', 'http://www.argentsolar.com', None, 'https://www.olivegarden.com/locations/az/chandler/chandler-fashion-mall/1561?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:chandler-az-1561_pl:locurl_rd:1432', None, 'http://www.chakobbq.com', 'http://www.mycleantastic.com', 'https://www.canadianappliance.ca/Showroom/Canadian-Appliance-Source-Calgary', 'https://locations.wendys.com/united-states/az/chandler/1045-s.-arizona-ave', 'http://www.chezcora.com/scarborough', 'http://www.vanlawfirm.com', 'https://store.vioc.com/nc/mint-hill/9020-lawyers-rd-28227-BD2902', 'http://www.mylittledumplings.com', 'https://www.kilwins.com/madison', 'https://tottoriallergy.com', 'https://www.brooklynbedding.com/showrooms/arizona/fountain-hills/?utm_source=yelp.com&utm_medium=referral&utm_campaign=yelppage', None, 'http://thepickledpeach.com', None, 'http://www.sonorancycles.com', 'http://hamptoninn3.hilton.com/en/hotels/alberta/hampton-inn-and-suites-by-hilton-calgary-university-northwest-YYCHSHX/index.html?SEO_id=YELP-HP-YYCHSHX', 'http://www.sparkleanlaundryphoenix.com/', 'http://www.wildlifeworld.com', 'http://www.gamestop.com/store/us/az/tempe/3674/tempe-marketplace-gamestop', None, None, None, None, 'http://www.the-dhaba.com', '1592409496', None, None, 'http://www.findlayvolvocarslv.com', 'https://www.dunninsurance.net', None, None, 'http://www.microsoft.com', 'http://www.deakspub.com/', 'http://www.fontesmd.com', 'http://sonoranvistadentistry.com', 'https://antechhair.com', None, 'http://fitnesspluscalgary.ca', None, 'http://www.nellisauction.com', 'http://www.avalonacademy.ca', 'http://www.arrowheadfamilydentistryaz.com', 'http://www.accessclarkcounty.com/', 'https://www.supercuts.com/locations/pa/shaler/shaler-village-haircuts-81039.html', 'http://www.fye.com', 'http://derkaffeekuchen.com', 'http://www.brkfst.co', 'http://www.onyourfeetaz.com', 'http://railroadbrewingcompany.com', 'https://thimblebeessewingschool.com', 'http://viphealth.ca', 'http://www.forevergoodasiancuisine.com', None, None, 'http://www.alignlv.com', 'https://stores.dickssportinggoods.com/pa/pittsburgh/42/', 'http://aureliospizza.com', 'http://www.starbucks.com', 'http://www.greencheeksdiaperservice.com/', 'http://www.sunupconstruction.com', 'http://www.fantasticsams.com', None, 'https://www.capricamelback.com', 'https://www.onehourheatandair.com/phoenix/', 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://Sitnstayover.com', 'http://www.wilsonstaekwondo.com', 'http://www.TheBuildABrainProgram.com', 'http://www.thornhillbodymassage.com', 'https://agents.allstate.com/the-valley-west-agency-surprise-az.html?cid=LDR-YP-CF-200318:AGL&Campaign=222230000015670', None, '1592409659', None, None, 'https://www.haptonline.com', '1592409672', None, None, '1592409685', 'https://www.simonmed.com/locations/all/simonmed_imaging___thompson_peak', 'http://www.animalmedicalandsurgical.com?utm_source=yelp&utm_medium=Business&utm_campaign=AnimalMedical&SurgicalCenter-CallNow', 'https://willoandroot.com', 'http://www.oldmilltoronto.com/spa', 'https://www.peopleready.com/locations/gilbert-az-1209', 'http://www.AuraSutra.com', 'https://www.haircutmenmatthewsnc.com', None, 'http://www.outtoday.com', 'http://stevesmeats.ca', 'https://www.wellsfargo.com', 'http://www.ahmassagetherapy.com', None, None, 'https://gilbert.puzzleeffect.com', '1592409735', 'http://www.warraichmeats.com/', 'http://www.greatlasvegashomes.com', None, None, 'http://www.westusa.com/Office-Detail/west-usa-realty-scottsdale/55046-7935840/', 'https://www.bold3dbrows.com', None, None, 'http://www.kedarhairinc.com/', 'https://dealer.sprint.com/experts-choice', None, None, 'http://www.midwifealliance.ca', 'https://highlyattunedtouch.com', 'http://www.thebrazillteam.com', 'https://studiomoviegrill.com/Locations/Arizona/Scottsdale?utm_source=yelp&utm_medium=organic&utm_campaign=yelp&utm_content=Scottsdale', 'http://www.usquaredental.com', 'https://www.docpopcorn.com/doc-popcorn/location-finder/charlotte-premium-outlets.html', 'http://www.cousinssubs.com/store/cousins-subs-madison-washington-ave', None, 'http://www.glammedspa.com', 'http://vivaphx.com', None, 'http://www.collegetowntempe.com/the-link-tempe.html', None, 'https://www.frysfood.com/storeHours?store=66000070', 'http://www.starbucks.com/store/8167/', None, None, 'http://www.palomino1.com', 'http://johnnyrockets.com', 'http://www.tuffshed.com/las-vegas-area/', 'http://m.primarycarewalkinmedicalclinic.com', 'https://www.jugojuice.com', 'http://www.massageheights.com/crocker-park', 'http://www.fiberfactory.com', 'https://www.singerpistiner.com', None, 'https://tinirestaurant.ca', 'http://www.antoinelaoun.com', None, 'http://www.tradervicsscottsdale.com', 'http://www.agritopia.com', 'http://www.thestuffedpepper.net', None, 'http://www.allegro-apts.com', 'http://firstplacecoffee.com', None, 'http://www.erdscalisoulfood.com', 'https://risasdental.com/find-a-location/westgate/?utm_campaign=LocationPage&utm_medium=WestgateYelpWebsite&utm_source=Yelp', 'http://www.citylinemoving.com', 'http://www.peterselectric.com', 'http://elizabeth.burnbootcamp.com', 'http://ashleywomenscenter.com/', 'https://www.walmart.com/store/2632/phoenix-az/details', 'http://locations.michaels.com/az/mesa/2778/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'https://comidaclt.com', 'http://www.goochi-pooch.com', 'https://www.henrys.com/stores/7-Scarborough.aspx', 'http://sincitybarbershop.com', 'http://www.clevelandymca.org/warrensville-heights.html', 'http://sitmeanssitmadison.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.hogle.ca', None, None, 'https://www.flywheelsports.com/studio/scottsdale/stadium-cycling', 'http://pechmannmemorials.com', 'https://dstrailersllc.com', 'http://shangarry.com', None, 'http://chiropractorcarephoenixarizona.com', 'http://www.tuesdaymorning.com', 'http://www.atkinsonsmartialarts.com', 'http://habitatcaz.org', 'http://www.plymouthchurchucc.org', None, '1592409926', 'http://www.blazepizza.com', '1592409932', 'http://cannedcraftbeerfest.com', None, 'https://www.wingstop.com/location/wingstop-421-phoenix-az-85015/menu', 'http://www.portofsubs.com', 'http://www.teashop168.ca/', 'https://www.thepittsburghbanjoclub.com/wednesday', 'http://www.chilis.com/EN/Pages/home.aspx', 'https://bostonpizza.com/en/locations/sunridge.html', 'https://www.gianteagle.com/Pharmacy/', None, 'http://www.defygravity.us/charlotte', None, 'http://www.dsbg.org', None, 'http://shookkitchen.com', 'http://www.noonsbobacafe.com', 'https://www.phoenix.gov/parks/parks/skate-parks/pecos', None, 'http://www.sneakababypeek.com', 'http://www.laitaliankitchen.com', 'http://www.tangobistro.ca', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', 'https://www.mypoolplans.com/contact-us/', 'http://www.procollage.com', None, None, 'http://www.palms.com/pearl-theater.html?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.flamingkabob.com/', 'http://www.smokinghostsbbq.com', 'http://www.fifthroom.com', 'https://www.mardigrascostumeshop.com', 'http://www.grangernaturopathic.com', '1592410010', 'http://www.ciaowinebar.com/', 'https://locations.wendys.com/united-states/nv/henderson/4450-e.-sunset-rd', None, 'http://www.allweatherroofers.com', None, None, None, 'https://www.bankofamerica.com', 'http://www.ChicagoMotorCarsLV.com', 'http://www.wsoffices.com', 'http://www.theautoprotectors.com', 'http://readelectricaz.com/', 'http://www.surlatable.com', None, 'https://pizzanova.com/pizza-nova-vaughan-9960-dufferin-st/', 'https://shop.nordstrom.com/st/nordstrom-fashion-show#restaurants?cm_mmc=yelp-_-ycm-_-rest-_-26386', 'http://sunrisemountaindentalandorthodontics.com', 'http://www.audiologycharlotte.com', 'https://benjaminsbarbershop.net', 'https://www.gioninos.com/locations/oh-medina-203-lafayette-rd-44256', 'http://www.greenbushbakery.com', 'http://www.avalondayspavegas.com', None, None, None, 'http://www.jgumbos.com/cleveland/', '1592410066', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.cubeworks.ca', None, 'https://scottsdale-spiritual-energy-boutique.business.site', 'http://www.cavarestaurant.ca', None, None, 'http://www.phoenixpediatrics.com', 'https://newcrescentbrewing.com', 'http://skinthropology.com', None, 'https://dozysleep.ca', 'https://www.aamcolv-rainbowblvd.com', 'http://www.coldstonecreamery.com/stores/20030', 'http://www.icecreampatio.com', None, 'https://tours.asu.edu/tempe/wells-fargo-arena', None, 'http://sushifriends.ca', None, 'http://goodcaretransmission.com/', 'http://www.collision-reporting-centre.com', 'https://www.justaroundthecornerpetsitting.com', 'http://www.phoenixacupunctureclinic.com/', None, 'http://www.drschraw.com', 'http://orderuncletonyspizza.com', None, 'http://allaboutmeaz.com', None, 'https://www.glazedoughnutslv.com', '1592410148', 'http://peakskiandboard.com/', None, None, 'http://www.iconsalonlv.com', '1592410159', 'https://www.wyndhamhotels.com/hotel/14872?tel=18003291073&iata=00093785&cid=fe:di:20161220:yl:pp:dius:14872', 'http://www.ellascuisine.com', 'http://coolcuts4kids.com/salondetail/default.asp?salonid=66002', 'http://www.huaxin.us/english/Location-Cle.html', None, 'http://www.langolino.ca/', 'http://www.madisonsbar.com', None, 'http://www.jujuberri.com', None, 'http://www.liszewskiandassociates.com/', 'http://www.gianteagle.com', None, 'http://www.filibertos.com', 'http://www.sharppoolcreations.com', None, 'https://www.biolifeplasma.com/us/#/donation-center?centerId=48', 'http://www.monkboyer.com', 'http://www.shaolinarts.com', 'http://www.district-704.com', 'https://union.wisc.edu/visit/union-south', 'https://www.autorepairinlasvegas.com', None, 'http://apodacasglassanddoor.com', None, 'http://www.16-bitbar.com/cleveland', 'http://www.thebrasstap.com/mesa', '1592410225', None, None, 'http://www.ablebakerbrewing.com', None, 'https://www.officedepot.com/storelocator/az/phoenix/officemax-6319/', 'http://www.starbucks.com/store/9298/', None, 'http://www.7-eleven.com/?yelp=29384', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.candinas.com', '1592410252', None, 'https://www.starbucks.ca', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.craftsmantableandtap.com/', 'https://andyoncall.com/charlotte-nc/', 'http://www.licesupportsystem.com', None, 'http://www.davidweissdds.com', 'https://locations.usbank.com/index/arizona/scottsdale/north-scottsdale-road-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'https://dippindots.com/loc/ll/US/NC/Concord/8111-Concord-Mills-Blvd_', 'http://www.rhondarosefloral.com/', 'http://carpetplusrepair.com', None, '1592410285', None, 'http://A1airaz.com', 'http://catermeicecream.com', None, 'https://www.dollartree.com/locations/az/glendale/4709/', None, 'http://www.robselectricandhandymanservices.com', None, 'http://asylumrecordsaz.com/', 'http://www.lavillabakery.com', None, None, None, 'https://www.mmautosales.net', None, 'http://www.sirenmovingcompany.com', None, 'http://www.AllCleanNow.com', 'http://www.RiceLasVegas.com', None, 'http://www.buffalobillwings.com', None, 'https://www.cslplasma.com/locations/bonuscoupon1216/47/donation-center-3430-e-tropicana-avenue-suite-69-las-vegas-nv', 'http://locations.michaels.com/az/scottsdale/2864/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://mindbodynv.com', None, 'http://coffeetree.com/portfolio/shady-side/', 'http://theslingshotexperience.com', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.123ink.ca', None, 'http://cococochocolatiers.com', 'http://www.gallaghersaz.com', None, 'http://www.momdoc.com', 'http://jlevines.com', '1592410376', 'http://www.roseemporiumto.com', 'https://www.4thstreetpizza.com', 'http://patonthebackspa.com', 'http://lasvegaspianos.com', 'http://www.murrayavenuegrill.com/', 'http://azbootandsaddlerepair.com', None, 'http://www.buckle.com', 'http://www.eventsatrefinery.com/', '1592410403', 'http://www.pearldiver.to', 'http://www.olivaeats.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.jackinthebox.com/', None, None, 'http://Skin-voodoo.com', 'https://www.velofix.com', 'http://www.pjoreillysirishpubandgrill.com/', None, 'http://www.rockofagesvegas.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'https://cacao70.com/en/our-locations/toronto-premium-outlets', None, 'https://www.goldencorral.com/locations/589/golden-corral-us-highway-29-north', 'http://www.auvieuxduluth.com', '1592410459', 'http://www.askdrgoldberg.com/', 'http://coffeereligionlv.com', None, 'http://shortywagswings.com', 'https://dmcosmeticandwellnesscentre.com', 'http://www.dostalfuneralservices.com/', 'http://www.ccomp.ca', 'http://local.firestonecompleteautocare.com/ohio/cleveland/6874-pearl-rd/?lw_cmp=IYP_YPC_MLP_1694', None, None, '1592410488', 'http://www.definitysalon.com', 'http://www.fatherandsonaz.com', None, 'http://www.fortmillford.com', 'http://refresheskinstudio.com/', 'http://www.vegascapecompany.com', 'http://www.wujixuan.ca', 'http://www.gymandfit.com', None, 'http://www.highcalibertrainingcenter.com', 'http://www.aeropostale.com', 'http://www.flatratelisting.com', None, 'https://dealer.sprint.com/experts-choice', 'https://www.starbucks.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.searsauto.com/stores/6064', 'https://www.caninecountryclubaz.com', '1592410539', 'http://www.americanwildernesscampground.com/', None, None, 'https://www.choicehotels.com/nevada/las-vegas/ascend-hotels/nv104/rates', 'https://www.choicehotels.com/CN256?mc=blypypaf', 'http://www.marcs.com/stores/marcs-parma-parmatown-grocery-store-44129.aspx', 'http://www.kabobhousenc.net/', 'http://www.mingspagoda.com', None, None, 'https://stores.petco.com/oh/elyria/pet-supplies-elyria-oh-3831.html', None, None, 'https://bananarepublic.gap.com', None, 'http://www.cvsurgnv.com', 'http://www.orangepatch.com', '1592410579', 'https://www.wyndhamhotels.com/hotel/28414?tel=18885951878&iata=00093785&cid=fe:mt:20170424:yl:pp:MTUS:28414', 'http://www.1lovekitchen.com', 'http://www.honest1warmsprings.com', 'https://manolos-towing-services.business.site', 'http://www.OasisOrtho.com', 'http://earlybirdphx.com', None, 'http://www.lawnmowerman1.com', None, None, 'http://maiortho.com', 'http://www.aznewbath.com', None, 'http://www.lakeshorelearning.com', None, None, None, None, 'http://www.proviewautoglass.com', 'http://www.certifiedprinterrepair.net/', 'http://a1officesolutions.com', 'http://vegasvalleyintro.com', '1592410632', None, 'http://phoenixdentistnearme.com/849-n-dobson-rd.html', 'http://janinasesthetics.com', 'http://salonandspaonmain.com', None, None, 'http://www.scottsdaleaz.gov/parks/srp.asp', 'https://www1.shoppersdrugmart.ca', 'https://www.intownsuites.com/extended-stay-locations/pennsylvania/pittsburgh/pittsburgh/', 'https://www.firstam.com/title/homebuilder/?utm_campaign=homebuilder-local-search&utm_medium=organic&utm_source=yelp&utm_content=arizona', 'http://www.puresalonaz.com', 'http://www.muirfieldpetclinic.com/', 'http://www.monroenissan.com/?utm_source=yelp&utm_medium=business_url&utm_campaign=local-citations', None, 'https://newhousehunters.com', 'http://www.nycsole.com', 'http://www.knitca.com/', 'http://www.smallanimalhousecalls.com', '1592410675', 'https://www.maverickhelicopter.com', 'http://www.annaslinens.com/?utm_source=Yelp&utm_medium=Annas_Homepage&utm_campaign=Yelp', None, 'http://myyogastudio.ca/', None, 'http://www.litchfieldparkpool.com', 'http://www.evolutionmotorsportsnv.com', 'http://www.roma910.com', 'http://www.kingrealty.to', 'http://vapingaristocrats.com/', 'http://www.montanas.ca', 'http://uflysimulator.ca/', 'http://www.terroni.ca/', 'http://www.partycity.com', 'http://www.sillygoosekids.com', 'http://integrativeaesthetics.gettimely.com', 'http://www.merlenorman.com/', None, 'http://www.aandeanimalhospital.com', 'http://www.torontopubliclibrary.ca/branch-detail.jsp?R=LIB031&eT=3', 'http://vbarbershop.com/locations/arcadia-phoenix/', None, 'http://www.arbys.com', '1592410730', 'http://www.7-eleven.com/?yelp=29384', 'http://www.splishsplashclean.com', 'http://www.bubbles.ca', 'https://www.get-locksmith.com/lasvegasnv', 'https://www.thebrick.com/pages/store-college-park', 'http://www.tropicamango.com', 'https://www.ediblearrangements.com/fruit-arrangements?utm_campaign=StoreID336&utm_medium=Listing&utm_source=Yelp', 'http://shopsys.ca', 'http://Act1realtyinc.com', 'http://www.eyelashextensionsaz.com/', '1592410758', 'http://www.scotiabankarena.com', 'http://www.shikiji.ca', 'https://www.jacksonhewitt.com/Tax-Preparation-Services-Locations/PA/McKees-Rocks/15607/', 'http://www.logomagik.com/', 'http://www.drinkbambu.com', None, 'https://www.mhmproperties.com', 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store143', 'http://www.mark-taylor.com/arizona/san-portales?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.bk.com', 'http://www.beddrs.com/', 'http://www.proactiv.com', None, None, 'http://www.thejewishcollection.com', 'http://www.theboulders.com', 'http://www.sundancedayspa.com', None, None, None, 'https://paddyo.com', None, 'http://www.harborfreight.com', 'http://www.clarksportsmed.com', None, 'http://www.azelly.com', 'https://www.planetfitness.com/gyms/north-scarborough?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://naturalmedicineanddetox.com/juice-bar-2', 'https://www.maxtour.co', '1592410828', None, None, 'http://abbeycats.org', 'http://www.protection1.com/local/arizona/home-security-az-phoenix', None, 'http://www.wookiestyleaz.com', None, 'http://www.sparksmoving.com', 'http://www.trivestdev.com', 'http://www.tjf-law.com', 'http://www.our-place.us', 'http://www.fredperry.com', None, None, None, 'http://storelocator.pepboys.com/pepboys/stores/las_vegas/east_charleston/00685', 'http://www.arizonapropane.com', 'http://northphoenixid.com', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://allstarzbarbershop2.business.site', 'http://www.aaronpaternoster.com', None, 'http://wildwestchildrensdentistry.com', '1592410884', 'https://guschlbauer.ca', 'http://www.grapevine.wine', 'http://lushusa.com', 'http://www.gyntoday.com', 'http://www.melissareikilady.com/', 'http://www.bigbonebbq.ca/whitby', None, 'http://www.bokapizza.com', 'http://www.harrisblvdveterinaryclinic.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=jan16', 'http://www.simonchiro.org', None, 'https://www.lifetime.life/life-time-locations/on-mississauga.html?utm_medium=directory&utm_source=yelp&utm_content=homepage', 'https://www.jugojuice.com', 'http://www.bestgyro.com/', 'http://blackrocpm.com', 'http://highrollerdeli.com/', '1592410928', 'http://recycler.car-part.com/AllJapanese/', 'https://www.antheminjurylaw.com', 'http://www.cosmoprofbeauty.com/', 'http://www.starbucks.com/store/9681/', 'http://stores.kay.com/az/phoenix/9617-n--metro-pkwy--w-.html', 'http://www.rockpaperbloom.com/home.html', 'http://nativegrillandwings.com/location/phoenix-tatum-bell/', 'http://www.babyfacellc.com', None, None, 'http://www.no1chineseglendale.com', 'http://www.coffeeculturecafe.com/locations/', None, 'http://www.leslieslaundrycare.com', None, 'http://www.sdsdental.com', 'http://www.milltanning.com', 'http://www.rexall.ca/', 'https://www.amresupply.com/locations/scarborough', 'http://deutschtownmusicfestival.org', 'http://www.olympic76pizzacafe.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://hdouglasdentistry.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLTPV', 'https://www.jerseymikes.com/22001', None, 'http://www.cuyahogalibrary.org/Branches/Middleburg-Heights.aspx', None, 'http://www.fawic.org', 'http://www.hellriegelsinn.com', 'http://www.ziggyscleaningservices.com', 'https://local.fedex.com/az/phoenix/office-5048/', 'http://Www.lowes.ca', None, None, 'http://www.logansroadhouse.com', 'http://palazzonailloungegilbert.com', 'http://www.starbucks.com/store/9298/', 'https://www.luckybrand.com/on/demandware.store/Sites-LuckyBrand_v2-Site/en_US/Stores-Details?StoreID=42569', None, None, None, None, 'http://www.ventureoutdoors.org', 'http://www.tranquilitystudio.com', 'https://stores.jcpenney.com/az/phoenix/clothing-stores-phoenix-az-2846.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2846', None, None, 'https://www.mobilityworks.com/locations/wheelchair-vans-for-sale-in-charlotte-north-carolina', 'http://studiopictor.com', 'http://www.bulkbarn.ca/en-ca/index.html', 'http://www.abideyogacleveland.com/', 'https://www.oliverestaurant.ca', 'http://www.quiktrip.com', 'http://scorpionkingexterminating.com', 'https://www.jerseymikes.com/2053', 'http://www.wakelingauto.ca/', None, 'http://1047kissfm.iheart.com', None, 'http://robertandjaysonmillerfinejewelry.com', None, 'https://marylynnspa.com/scottsdale/', None, None, None, None, 'http://www.philippelusi.com/', 'https://sunsetstation.sclv.com/Entertainment/Strike-Zone/?utm_source=YELP&utm_medium=SOCIAL&utm_term=SS&utm_content=SS-PROPERTIES&utm_campaign=SS-YELP', 'http://www.starbucks.com/store/14175/', 'https://www.succuterra.ca', None, None, 'http://www.perkcupcafe.com/', 'http://www.damshortfilm.org', 'http://www.killhamlaw.com', 'http://www.structube.com', None, None, None, 'http://www.bmv.ohio.gov/contact.stm', None, 'http://www.theabacusinnarrowhead.com', None, 'https://client.schwab.com/public/branchlocator/branchdetails.aspx?localdir=yelp&branchid=1284', None, None, None, 'http://www.learningexpress.com/store/madison/', 'http://www.sushibelle.com/', 'http://kupfertandkim.com', 'http://www.royalthreadingstudio.com', None, 'https://kiddieacademy.com/wexford/?utm_source=yelp&utm_medium=referral&utm_content=listing&utm_campaign=Sponsored+Listing', 'http://www.petsmart.com', 'http://www.uptownalleysurprise.com', 'http://www.karachigrill.ca/', 'https://www.take5oilchange.com/locations/oh/parma-137/', 'http://www.embassynightclub.ca/', 'http://www.eastlandmall.com', None, None, None, 'http://www.sipshucksip.com', 'https://www.hilton.com/en/hotels/lashnhx-hampton-suites-las-vegas-henderson/?SEO_id=YELP-HP-LASHNHX', 'http://www.rrpl.org', 'https://infinitysolarlasvegas.com', 'http://porkopolisbbqaz.com/scottsdale-porkopolis-bbq', None, 'https://locations.wendys.com/united-states/al/madison/8814-hwy-20-w', 'http://www.phoenixcosmeticdentalcare.com', 'http://www.topothemornindonuts.com', 'http://www.samjamescoffeebar.com', 'http://www.sacredsteelaz.com', 'http://www.citysearchcalgary.com', None, None, 'http://scarborough.handymanconnection.com', 'http://www1.shoppersdrugmart.ca/en/store-locator/store/774', '1592411233', 'https://agent.amfam.com/sean-stewart/nv/henderson/2520+saint+rose+pkwy/', None, 'http://deedar.ca', 'http://azyunrestaurant.com', 'https://www.EarnhardtBuickGMC.Vegas', 'https://www.valleypain.org/locations/offices', 'http://theneighborhoodgarage.com/', None, 'http://www.littleshmiddyshotmeathouse.com/', 'http://www.queencitylumber.com', None, 'https://www.solismammo.com/arizona/paradise-valley', '1592411281', 'https://www.discounttire.com/store/az/gilbert/s/1418?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', None, None, None, 'http://www.evans-air.com', 'http://www.eq3.com', None, 'https://www.crystal-springs.com', 'http://www.papamurphys.com', 'http://www.indigo.ca', None, None, 'http://homewoodsuites3.hilton.com/en/hotels/arizona/homewood-suites-by-hilton-phoenix-scottsdale-SCTMVHW/index.html?SEO_id=YELP-HW-SCTMVHW', None, 'http://www.surabbq.com', 'http://www.affordablehomecare.com', 'http://www.mark-taylor.com/arizona/waterside/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://pickeringmarkets.com', 'http://www.epicplumbingaz.com/', None, 'http://www.collinslaw.net', None, None, 'http://www.camelbackfamilyplanning.com/', 'http://www.rottenrottie.com', 'https://www.9round.com/fitness/Henderson-NV-x3490', 'https://www.homedepot.com/l/Cornelius/NC/Cornelius/28031/3638?cm_mmc=seo-yelp&', 'http://www.lavolv.com', None, 'https://www.naturepedic.com/cleveland?utm_source=yelp&utm_medium=referral&utm_campaign=Cleveland%20OMG%20Yelp', 'http://imagesinternational.ca', 'http://www.luxornailsandspa.com/', None, 'http://carstarexpress.ca/locations/toronto/', 'http://franklygoodcoffee.com', 'http://www.bombshelllash.com', 'http://www.thedixiepigbbq.com', 'http://www.superdupercarpetcleaning.com', 'http://www.asliceofchicagolv.com', 'http://www.livahwatukee.com', None, 'https://www.maverickairlines.com', 'http://barrelhouseaz.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700006430627140&ds_s_kwgid=58700000443429122&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'https://locations.theupsstore.com/oh/berea/441-w-bagley-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.meant2beevents.com', None, 'http://www.originalmotorcycleburgers.com/', 'http://www.racersadvantagestore.com', 'https://www.beachclifftavern.com', 'https://royalindia-calgary.com', 'https://www.firehousesubs.com/locations/az/gilbert-gateway', None, None, 'http://www.whattapup.ca', 'http://lovemedobaby.com', 'http://www.karvestudio.com/locations/scottsdale/', 'https://www.maxxproperties.com/stonybrook-phoenix-az/', 'http://www.techshop.ws/ts_chandler.html', None, 'http://www.cruiseshipcenters.com/en-CA/KimberlyBodegom/home', 'http://www.swbehavior.com', None, 'http://stationdessports.com/fr/trouver-une-station/st-leonard.php', 'http://www.dos-amigos.ca/', 'http://medshapeweightloss.com', 'http://fureverpet.wix.com/furever', None, 'http://www.morethanfacesmedspa.com', 'http://www.tedbaker.com/us/stores/store/70092', 'http://havemore.business.site', 'http://www.westusa.com', None, 'https://firstinspection.com', 'http://hcws.org', None, 'http://www.zuzuspetalsaz.com', 'http://www.tocamd.com', 'https://www.erinmillsacura.ca', 'http://azrockit.com', 'http://local.slippymap.com/cinnabon/NV/89107/index.html', None, 'http://www.costco.ca/warehouse-locations/newmarket-east-gwillimbury-on-510.html', None, 'https://thecandlebar.co/pages/locations', 'https://www.sprint.com/storefronts/bd/sprint-surprise-az-85374-fcs-1005/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.econappliance.com/', '1592411592', '1592411595', 'http://www.coldstonecreamery.com/stores/21246', 'http://Www.allstarsbilliards.com', 'https://www.drivetime.com/Dealership/Find/arizona/phoenix/399?vend=yelp&source=local&reg=pho&camn=pho4&camt=nobran', None, 'http://www.theaccompanynv.com', 'http://www.durafoaminc.com', 'http://www.deserteducation.com', 'http://downtownsalonphoenix.com', 'http://www.rayfamilydentalcare.com', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___kyrene', None, 'https://www.phoenix.gov/parks/parks/skate-parks/desert-west', 'http://www.tjmaxx.com', None, None, 'http://www.autoairandelectric.com', None, 'http://www.dunkindonuts.com', 'http://www.lilyrosebridal.com', None, 'http://www.safeway.com', 'http://www.banfield.com/veterinarians/az/gilbert/gil?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://saharaanimalhospital.com', 'http://www.BestDentalofMesa.com', 'http://www.orthoyours.com/', None, 'https://nationwidevision.com/locations', None, 'https://locations.postnet.com/nc/concord/366-george-w-liles-pkwy-nw', 'http://www.mrformalaz.com', None, 'https://callorange.com/locations/locksmith-mesa-az/?utm_source=yelp&utm_medium=yelp', 'http://boulderstation.sclv.com/Dining/Guadalajara?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://advancedautoserviceandtire.com/tires-auto-repair-scottsdale-az-3', 'http://www.cannerycasino.com/dining/casa-cocina-restaurante-mexicano', 'http://www.feilersrestaurant.com/', None, '1592411730', None, 'http://toppers.ca/georgetown', 'https://agents.allstate.com/maria-miuccio-las-vegas-nv.html', None, 'http://churchaliveaz.com', 'http://www.tequilanightclub.com', 'http://www.fhevolutionsalonpgh.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.funnybone.us', None, 'https://nellisafb-nv-6208.theupsstorelocal.com/?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.countrykitchenrestaurants.com', None, None, 'http://www.ncbmx.com/', 'http://www.usps.com/', 'https://www.johnnyrockets.com', None, 'http://www.sungardenestates.org', 'http://www.pinkjeeptourslasvegas.com/', None, 'http://www.siennamercato.com', None, None, 'http://www.compassionatebeauty.com/', 'http://www.crystaltechwater.com', 'http://www.srocompanies.com', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'https://www.westvalleymed.com', None, None, 'http://www.josbank.com/AjaxStoreLocatorDisplayView?catalogId=14052&langId=-1&storeId=13452&utm_source=yelp&utm_medium=listing&utm_content=835&utm_campaign=NC', 'http://www.istanbul-grill.com', 'http://www.calgarycostume.ca', 'http://elconaz.com', 'http://www.homegoods.com/locator/?sessAddress=Aurora%2C+CO&storeid=455#map_top', 'http://www.jsullivantravel.com/', 'http://www.specsandspecsoptical.com', 'http://lasvegasmobilemassage.com', 'https://www.halibuthouse.ca', 'https://locations.usbank.com/index/nevada/north-las-vegas/ann-simmons-nv-albertsons-branch.html?utm_campaign=visit-website&utm_medium=business-listing&utm_source=yelp', 'http://medicalmassagescottsdale.com', 'http://phoenixvalleystorage.com', 'http://bibibop.com', 'http://www.warehousegroup.ca/el-furniture-warehouse-bloor-st', 'http://www.thecleaningauthority.com/northcharlotte', 'https://mandarinrestaurant.com/newmarket/', 'http://galaxie-madison.com', '1592411898', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=5358&localechange=1', 'http://www.lakshmahealinghands.com', None, None, 'https://www.spa810.com/arrowhead/?utm_source=Yelp+website', 'https://www.usps.com/', None, 'http://www.salsgrocery.com', 'http://www.estrellagolf.com', 'https://www.enigma1solutions.com', None, 'https://stores.joann.com/az/avondale/2132/', 'http://www.haikutokyo.com', None, 'http://www.sienahillsprimarycare.com/', 'http://www.pghjunk.com', 'https://www.ximiso.com', None, None, 'http://www.avalonhillsapartments.com', 'http://alicefazoolis.ca/locations-oakville/', None, None, None, None, None, 'http://www.tiltedkilt.com/locations/matthews/', 'http://www.bratopia.ca', None, 'http://www.pinballmuseum.org/', None, None, 'http://www.riceandco.com/ricerepublic/', None, 'http://www.plumbingpeoriaaz.com', 'http://www.covingtonapts.com', None, 'http://pizza-re.com', 'http://drrickdentistry.com', 'https://www.helzberg.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.kmart.com/stores/north-carolina/pineville/4777.html', None, 'https://www.lasvegashousingexperts.net', 'http://www.olosspa.com', 'http://wildwestdelivery.com', None, 'https://www.nike.com/retail/s/nike-factory-store-chandler', None, 'http://www.crystalcourtvegas.com/', 'http://www.superheropros.com', 'https://child-care-preschool.brighthorizons.com/AZ/Phoenix/coppersun', '1592412074', 'http://www.AutoVaun.com', 'http://www.sushitnt.com/', 'http://www.sisusalon.co', 'http://silvermountainrealestategroup.com', 'http://solutionsstaffing.com', 'http://www.thebeansprout.net', 'http://www.torontoathleticclub.com', 'http://locations.traderjoes.com/pa/pittsburgh/638/', 'http://www.drstoneaz.com', 'https://www.signaturestyle.com/locations/on/scarborough/first-choice-haircutters-5666.html', 'https://www.mybizniche.com', None, 'https://www.nofrills.ca/store-locator/Kevin%27s+NOFRILLS+Calgary/3155?storeId=3155', 'http://www.dreamproductions.com', 'http://guardianwindowcleaning.dev.thryv.com', None, 'http://www.whitehallparcapts.com', '1592412133', 'https://www.gerbercollision.com/locations/las-vegas-decatur-blvd-nv', 'http://fiveguys.com', 'https://vimtrim.com', 'http://www.robinsondentist.com', 'http://bqmburger.com/riverside/', 'http://www.djmikefox.com', 'http://rebeloil.com/', 'http://www.universalmedicaldata.com', None, 'https://www.longhornsteakhouse.com/locations/az/phoenix/phoenix-paradise-valley/5461?cmpid=br:lh_ag:ie_ch:dry_ca:LHQ121LOCURL_dt:20200615_sn:yelp_gt:phoenix-az-5461_pl:locurl_rd:1403', 'http://www.mullinspub.com/locations/kington-road/hours-location/', None, 'http://www.trackandfieldbar.com', None, 'https://www.hendrickbmwcharlotte.com/?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', 'http://maaco.ca/locations/on/brampton-12018', 'https://www.marcs.com/stores/marc-s-midtown-grocery-store-44134', 'http://www.americanjunkieaz.com', 'http://www.coldstonecreamery.com/stores/20181?latitude=33.6071829&longitude=-111.9403254', 'http://www.thewindmillrestaurant.ca', None, None, '1592412214', 'http://thesanddollarlv.com', 'http://www.canarysfamilyrestaurants.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.pecangrovevet.com', 'http://www.samazingskinservices.com', 'https://www.storagewest.com/facilities/gray-road/?utm_source=YelpCTA&utm_medium=referral&utm_campaign=gray-road-business', 'http://www.dominos.com', 'http://www.patioenclosures.com/sunrooms-pittsburgh.aspx', 'http://locations.michaels.com/AZ/PHOENIX/9922/', 'http://www.georgeonqueen.com', 'http://www.citi.com', 'http://www.ledelice.ca/index.htm/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'https://www.supercuts.com/locations/az/glendale/bell-park-shopping-center-haircuts-80215.html', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/15474+West+Greenway+Road-Surprise-AZ-85379/storeid=5477?cid=ps_ylp_2020', 'https://www.cellairis.com/store-locator', 'https://www.olivegarden.com/locations/oh/elyria/elyria-midway-mall/1770?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:elyria-oh-1770_pl:locurl_rd:1620', None, 'http://www.goodwillaz.org/', 'https://www.shopwss.com', 'http://www.valleyradiologists.com', 'https://lowestpricelawyers.com', 'http://www.jrfurnituregallery.ca', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', None, 'http://www.rotorooter.com/bouldercitynv', 'https://www.dlrichie.com', 'http://www.ansautodetail.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.shakomakogrill.com/entrees/', 'http://www.zydecobistrollc.com', 'http://www.delreycleaners.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', None, None, None, None, None, 'https://www.fredastaire.com/phoenix-north', '1592412378', None, 'https://www.onestoproofshop.com', 'https://www.bootbarn.com', 'http://www.mossberginjurylaw.com/', 'http://www.costco.ca', '1592412400', 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', None, None, 'http://www.cputopia.com', None, 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', None, 'http://www.desertbirkenstock.com', 'http://www.cariboucoffee.com', None, '1592412439', 'http://dentistrygastonia.com', '1592412446', None, 'https://www.donmillersubarueast.com', 'http://crumblcookies.com', None, 'http://www.gsbbqlounge.net', 'http://www.thegoldenchopstick.com/', 'http://evansimportservice.com', 'http://azautoglass.net/', 'http://www.gorillaradioonline.com', 'http://www1.toronto.ca/parks/prd/facilities/complex/2702/index.htm', 'https://www.walgreens.com/locator/walgreens-1725+northport+dr-madison-wi-53704/id=2967', 'http://www.desertexteriorlighting.com', None, None, 'http://www.ljsilvers.com/', 'http://www.gileadroadpedsandim.com', None, 'http://www.appliancerepairguys.ca', 'https://thehalsten.com', 'http://www.meineke.com/', None, 'http://www.deltahotels.com', '1592412525', 'http://www.myplasticsurgerytoronto.com', 'http://www.coffeejazzmixers.ca', 'http://www.blueberryhillrestaurants.com/', 'http://lvsmile.com/', None, 'http://www.joemamas.ca', 'http://www.teaopia.ca', None, 'http://www.iwannaglo.com/', None, 'http://www.betterlifemobility.com', 'http://www.sociallyposted.com', 'http://berani.ca', 'http://www.rougepark.com/index.php', 'https://www.peaceloveandlittledonuts.com/bethel-park-pa', 'http://solaceskymassage.com', 'https://www.garagecabinetsbyeric.com', 'http://www.mrsewing.com', None, None, 'http://popeyeschicken.ca/', 'https://local.fedex.com/az/avondale/office-1427/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.foxchapeldentistry.com', None, None, 'http://www.ariosorentals.info', None, None, 'http://regissalons.com/salondetail/default.asp?salonid=3861', None, None, 'https://www.canyonstatecu.org', 'http://www.upmc.com/services/urgent-care/locations/pages/monroeville.aspx?curloc=&daddr=40.439533,-79.765892c.com/services/urgent-care/locations/pages/monroeville.aspx?curloc=&daddr=40.439533,-79.765892', 'http://www.lauriemyersyoga.com', 'http://www.halorestaurant.com/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, None, 'http://www.gastonfarmersmarket.com', None, 'http://viajerocantinatoronto.com', 'http://www.myreserveapartments.com', None, 'http://www.pooltroubles.com/', None, 'https://www.simonmed.com/locations/all/simonmed___goodyear', '1592412708', None, None, 'https://italvitalrastarant.com', '1592412721', 'http://www.consignmentgallery.ca', 'http://www.markvillefitness.net/', 'http://mortimergreatsmiles.com', None, 'https://www.pensaitaliano.ca', 'http://www.playcious.com', 'http://motelbouldercitynv.com', 'https://stores.loft.com/outlet/us/nv/las-vegas/7400-las-vegas-blvd-south.html', 'http://www.mainstreetbeerbbq.com', 'http://www.4cjcleaningservice.com', 'http://www.mainstreetmech.com', None, 'http://www.freezinglakespools.com/', None, None, None, None, 'http://www.oaklandnailsllc.com', None, None, 'http://www.carrlawaz.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.fxfitnessclubs.com/maple-heights', None, 'https://local.skechers.com/az/tempe/10', 'https://www.villettaapartments.com', 'http://www.babystackscafe.com/', None, 'http://www.nevesgroup.com', 'http://www.perfectthreading.com', 'http://www.paramountequity.com', 'http://qdoba.com', 'http://www.bk.com', None, 'http://www.mojaveac.com/', None, '1592412858', None, 'http://www.arizonaav.com', 'http://legacymga.com', None, 'http://www.sushimountain.com', 'http://www.pourtaproom.com', None, 'http://www.autozone.com/storelocator/storeLocatorMain.jsp?targetPage=storeLocatorMapHours&store=406', None, None, 'https://www.redrobin.com', 'http://www.treatyourselfcakes.com', 'https://locations.panerabread.com/sc/indian-land/7756-charlotte-hwy.html', 'http://www.t-mobile.com', 'http://www.townandcountryshops.com/location/', 'http://www.desertridgepros.com', 'https://foreverhomelv.com', 'http://www.restorationhardware.com', None, 'http://www.altezalabs.com', 'http://www.sugartiers.ca/', 'http://maxsportsgrille.com', None, None, 'http://www.joycefactorydirect.com/', None, None, '1592412959', None, 'https://www.caesars.com/flamingo-las-vegas/things-to-do/bugsys-bar?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=BugsysBar&utm_content=bar', None, None, 'https://encantofamilyaz.com', 'http://www.villamontanaapartments.com', 'http://www.eggsmart.ca', 'http://www.nvbc300.com', None, None, 'http://vivamexiconorthroyalton.com/index.htm', 'http://www.activehealingcentre.com', None, None, 'https://rubsmassage.com/locations-rubs-massage/store/4981-s-arizona-ave-no-2-chandler-az-85248/', 'http://www.juicetownjailhouse.com', 'http://shastapools.com/', 'http://www.delriolodge.com/', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=1', 'http://www.cureallplumbing.com', None, None, 'http://www.crcchiro.com', '1592415265', 'http://www.starbucks.com', 'http://osal.ca', None, 'http://www.kyliessportsbar.com', 'http://www.postersmostly.com', None, 'http://www.precisiontuning.ca/', 'http://www.goldenbakerync.com', None, '1592415302', 'http://www.kettleheroes.com', None, 'http://www.allstarwingsandribs.com/', 'https://locations.wendys.com/united-states/nv/henderson/4450-e.-sunset-rd', 'http://www.pizzahut.com/', '1592415325', 'http://www.suzukiofnewmarket.com', 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=555', 'https://lightsoftheworldus.com', '1592415339', 'http://www.logbarn.ca', 'http://www.homegoods.com/tjx/store.aspx?id=444', 'http://lakeshoreeatery.food-places.com', 'http://www.philippelusi.com/', '1592415359', 'https://locator.chase.com/il/peoria/7707-n-knoxville-ave?jp_cmp=rb/LocalListings/aff/branch/na', 'http://clickserve.dartsearch.net/link/click?lid=43700044282967588&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.tlcpest.com', None, 'https://uoficreditunion.org', None, None, 'http://www.tricityeastvet.com', 'http://www.rajdoot.ca', 'http://www.laborgataapartments.com', None, 'http://namcoarcade.cf', 'http://www.yumys.ca', 'http://www.chandlercinemas.com', 'http://www.visions.ca', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://lvh2o.com', 'http://www.silverspoongta.com', 'http://www.vedatakeout.com', 'http://theedgewater.com/dining/the-icehouse/', 'https://www.doggiedistrict.com?utm_source=yelp&utm_medium=social', None, None, 'http://www.pebblecreekgolfaz.com/', 'http://shoprivergate.com', 'http://www.collegehunkshaulingjunk.com/locations/cleveland-oh', None, 'http://www.RealEstateKnoke.com', '1592415428', 'http://www.nextlevelpoolservices.com', 'http://rayraysfinefoods.com', 'http://www.floridatile.com', 'http://sitstaydogemporium.com', 'https://locations.monro.com/pa/pittsburgh/4844-mcknight-rd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, None, None, None, 'http://www.orleanscasino.com/entertain/orleans-showroom?disid=wmm_yelp_to_corporate_orleansshowroom_organiclink', 'http://po-chicken.business.site', '1592415457', 'http://www.apollodrycleanerstempe.com', 'http://www.worldbeverageliquorstore.com', None, None, 'http://www.alaschools.org/arizona/az-schools/gilbert-north-7-12', 'http://www.edithsfashions.com/', 'http://www.prestopanini.ca', None, 'http://www.marriott.com/hotels/travel/yyztv-residence-inn-toronto-vaughan', None, 'https://www.gracefootmassage.com', 'http://www.mackenzieshighpark.com', None, 'https://www.wingstop.com/location/wingstop-1532-parma-oh-44129/menu', 'http://www.cltpediatricdentistry.com/', 'https://johnwongs-restaurant.com', 'http://sorrentoristorante.ca', None, 'http://www.loannnailsspavip.com', None, 'https://www.alexandraalterations.com', None, 'http://www.wecellphonesandmore.com/', None, None, 'http://www.bebe.com', 'http://www.wedoitpools.com', 'http://www.amagickalmoon.com', 'http://forbeschiropracticlasvegas.com', 'http://www.zikiz.vegas', None, None, 'http://www.dionnesmeats.com/', None, 'http://seven-east.com/home.html', None, 'http://psburgh.com', None, 'https://www.americafirst.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://whasn.com/locations/whasn-central', 'https://6-angels-towing-service.business.site', 'https://www.pteglv.com/locations/pts-gold/st-rose-eastern/', None, 'http://panagios.ca', 'http://www.angeliasitaliangrille.net', None, 'http://www.806cleveland.com', 'http://www.pittsburghweddingdjservice.com/', 'http://www.eyetique.com', 'http://www.redskygallery.com', '1592415577', None, 'https://www.dollartree.com/locations/az/glendale/4709/', 'http://C21vegas.com', None, 'http://rareearthwine.com', 'http://pizzaville.ca', 'http://www.glassreplacements.com', 'http://www.bankofamerica.com', 'https://www.petsmart.ca/stores/ca/on/whitby-store0934.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', None, 'http://www.fabulashz.ca', 'http://www.pussykatvegas.com', 'http://gardeniabridal.com/', None, 'https://www.canadiansprings.com', 'http://www.homesolutionsbylibny.com', None, 'http://www.notion-design.com', 'http://www.desertsageapts.com', 'http://www.starskycanada.com/', 'http://www.deltechcs.com', 'http://barlowmotors.com', 'http://888junkvan.com', None, 'http://allurenailbar.ca', None, 'http://www.azmtba.com', 'http://www.companionahlv.com', 'https://sweetfrog.com/locations/store/sweet-frog-stow-oh', None, 'https://www.jerseymikes.com/3096', 'https://thrifty.com/loc/ll/CA/AL/CALGARY-(AL)/927~6-AVE-SW', 'http://www.mathnasium.com/redrock', 'http://goodnightsleepsite.com', '1592415659', 'http://www.HelpingHandsAuto.Org', None, 'http://cycle-ave.com', None, 'https://solidrockstructures.com', 'https://shawarmaville.ca', None, 'http://www.sunaway.com', None, None, 'http://www.thenookieshop.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, 'https://www.precisiontv.com', 'http://pricelessplumbing.com', 'https://www.lifetime.life/life-time-locations/az-phoenix-north-scottsdale.html?utm_medium=directory&utm_source=yelp&utm_content=homepage', None, 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=578', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=13514&localechange=1', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB01', 'http://www.bbfw.com', None, None, None, None, None, 'http://mschantellesdaycare.wix.com/cw', None, 'https://www.nashpowersportsscottsdale.com', 'http://microsoft.com/en-us/store/locations/oh/beachwood/beachwood-place/store-37?pointit_retailsustain_sitelinks_Yelp', 'http://www.desertorthopedicspecialists.com', None, 'http://www.thermalprosac.com', 'http://www.acuvegas.com', 'http://thesagehairstudio.com', 'http://www.thefixandco.com', 'https://www.walgreens.com/locator/walgreens-2010+branch+st-middleton-wi-53562/id=10555', 'http://brianaleephotography.co', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85306/214-in-glendale/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-214&utm_content=website-link&howheard=IYE', None, 'https://www.planet-nissan.com', 'http://www.neuroandbrain.com', 'http://www.thebbqpro.com/', None, 'https://www.ganleyvillagechryslerdodgeram.com', 'http://www.streetsofnewyork.com', 'http://www.svengalisalon.com', 'https://www.summerlin-selfstorage.com', 'http://www.walkerspethotail.com', None, '1592415781', 'http://www.stanleysteemer.com', 'http://www.seasaw.net', 'http://www.threelittlebirdsinc.com', None, 'http://www.big5sportinggoods.com', 'http://www.stevemadden.com', 'http://www.spiritualconnectionslv.com', 'http://www.coldstonecreamery.com', 'http://www.letsgooffroad.com', None, 'http://www.als-donuts.com', None, '1592415811', 'http://www.beanthru.com', '1592415816', 'http://www.veronafamilydental.com', None, 'http://www.superendo.com', None, None, 'http://www.porcelainroom.ca', 'http://www.qcbooths.com', None, None, 'https://www.wyndhamhotels.com/hotel/46495?tel=18885953511&iata=00093785&cid=fe:wg:20170523:yl:pp:winca:46495', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, 'http://greencleanarizona.com', 'http://www.costeffectiveroofing.com', 'http://www.brightideaschildcare.com', 'http://www.spicecaters.com', None, 'http://www.dundaswestvets.com/', None, 'https://www.ahn.org/location-detail?type=Diagnostic_Testing_&name=Pine_Hollow_Medical_Associates', 'http://synergyptnv.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXBC', 'https://www.cvoeyecare.com', None, 'http://www.4sistershop.com', 'http://www.venetian.com/hotel/attractions/gondola-rides.html', None, None, None, None, None, None, 'http://www.u-wrench.ca/', None, 'http://thecuppacoffeebar.com', None, 'http://www.omega-gyros.com/', None, None, None, None, None, None, 'https://www.cage.ca/laval', 'http://www.JimmyJohns.com', None, 'http://www.thaigardenajax.ca', 'http://www.superpantry.com', None, 'http://www3.ttc.ca/Routes/505/Eastbound.jsp', 'http://www.bonairproducts.com', None, None, 'http://www.fitchburgvet.com', 'https://ca.dresden.vision', None, None, 'http://henhousetoronto.com', 'http://www.sushikiku.com', 'http://www.cafe-86.com', 'https://locator.chase.com/nv/henderson/637-n-stephanie-st?jp_cmp=rb/LocalListings/aff/branch/na', 'https://www.imsaz.com/', 'http://www.doctor-hill.com', '1592415967', None, None, 'http://www.seescapeto.com', None, 'https://www.gowireless.com/stores/pa/squirrel-hill/squirrel-hill-forbes-avenue/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1850+West+Franklin+Boulevard-Gastonia-NC-28052/storeid=3823?cid=ps_ylp_2020', 'http://www.valleywideglass.com', 'https://bluestonelane.com/coffee-shops/downtown/', 'http://www.cooksvillehyundai.com', 'http://www.starbucks.com', 'http://www.firstchurch.church', 'http://conginspizza.com', None, None, None, 'http://www.shakatronicsav.com', '1592416003', '1592416006', 'http://www.tascanada.com/', 'https://www.zandersolutions.com/madison-wisconsin-basement-waterproofing/', 'http://www.sundariphotography.com/', 'http://dirtbelly.com', 'http://yorkmontcafe.com/', '1592416023', None, 'https://www.advantagestorage.net/self-storage/az/surprise/advantage-storage-west-yorkshire/', 'http://www.AmeraPestControl.com', 'http://www.colehaan.com', 'https://locations.theupsstore.com/nc/charlotte/2820-selwyn-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://locations.massageenvy.com/north-carolina/charlotte/8020-providence-road.html', 'http://www.wallywaffle.net', 'http://www.harveys.ca/', 'http://www.blueandwhitetaxi.ca', 'http://www.jinglestoo.com/boccone/', 'http://top10automotive.com', 'http://www.beachersmadhouse.com', 'http://www.canyonsuites.com', 'http://www.limojohnny.com', None, None, 'http://www.chopsticknc.com/', 'http://www.peterpiperpizza.com', None, 'http://www.partycity.com', 'https://reservations.mgmmirage.com/bookingengine.aspx?host=hotel&pid=938&utm_campaign=yelp_cta&utm_medium=general&utm_source=vdara_cta', 'http://www.lapazcharlotte.com/', None, 'http://www.soldiablocantina.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4909+Paramount+Boulevard-Lakewood-CA-90713/storeid=5014?cid=ps_ylp_2020', None, 'https://storexpressselfstorage.com/robinson/units', 'http://www.kikurevolvingsushi.com/', None, 'http://www.laurenreidmua.com', 'https://oceanpacificwatersystems.com', '1592416109', 'http://www.hotshotaz.com', 'http://whellermdpa.com', 'http://www.trevorkitchenandbar.com', None, None, None, None, 'http://dedezmakeup.com', 'https://sossprinklerrepair.com', 'https://mountainsidefitness.com/locations/carefree/', 'https://www.searshomeservices.com/locations/appliance-repair/oh-north-olmsted/5000-great-northern-mall', 'https://store.vioc.com/nc/charlotte/4511-randolph-rd-28211-BD2901', None, 'https://www.cricketwireless.com', 'http://aroundtheworldcafe.com', None, 'http://www.sprucetreemusic.com', None, 'http://www.prestigecare.com', 'http://www.gijoevstransformers.com/', 'http://www.danielstotalcarcare.com', None, 'http://www.holidayinn.com/hotels/us/en/phoenix/phxno/hoteldetail', 'http://www.tlsautoservice.com', None, 'https://www.speedycash.com/find-a-store/nevada/las-vegas/flamingo-and-jones?utm_source=yelpstorelocator&utm_medium=Affiliate&utm_content=afflink', 'https://www.kaikaki.ca', 'http://radimed.ca/fr/cliniques/westmount-square', 'http://www.mariscoscamaronpelao.com', None, 'http://www.oaktreevet.net/', 'http://www.bk.com', None, None, None, 'http://hersheysofhudson.com', None, 'https://helmkenplumbing.com', 'http://www.jbmpatrol.com', 'http://www.signsbytomorrow.com/pittsburgh/', None, 'http://www.williamashley.com', 'http://www.7-eleven.com/?yelp=29663', 'http://www.danielallendds.com/', 'https://www.metro.ca/en/find-a-grocery/329', None, '1592416269', 'http://www.southpaw-pgh.com', 'http://www.madrose.pub', 'http://www.arrowheadtownecenter.com', '1592416284', 'http://www.thegreatoutdoorscalgary.ca', 'http://www.parcdispensary.com', 'http://www.gentrypoolrepair.com', None, None, 'http://www.delamer.ca', None, 'http://www.ashcroftandoak.com', 'https://www.optumcare.com/state/specialty-care/specialist-locations/fort-apache-oncology.html', 'http://CanadaUnlocking.com', 'http://www.trove.ca', 'http://calibercollision.com/locate-a-caliber-collision-center/matthews', 'https://www.aspendental.com/dentist/pa/homestead/240-waterfront-dr-e?utm_source=yelp&utm_medium=lociqyext&utm_campaign=Homestead%2CPA%7C%7CHomestd_PA%7C%7C1103&utm_content=listing', 'http://www.eat-at-create.com', None, 'http://fuelpizza.com', 'http://www.blissfulyoga.net/', '1592416345', 'http://www.apollocafepittsburgh.com/', 'http://www.drtroysmiles.com', 'https://www.crunch.com/locations/phoenix?utm_source=Yelp&utm_campaign=YelpwebsitePhoenix', 'http://www.wisecountybiscuits.com', 'http://www.drlagers.com/', 'https://www.applebees.com/en/restaurants-madison-wi/4710-east-towne-boulevard-87065', 'http://www.tailwaggerstoronto.com', 'http://www.palmcrestliving.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', None, None, None, None, 'http://www.philippelusi.com/', 'http://highimpactlv.com', 'http://www.cal-am.com/communities/san-estrella', 'https://liwindow.com', None, 'http://niedshotel.myfastsite.net/', None, 'http://champaigndentist4u.com/', 'http://mainstreetburgers.ca', 'http://www.hoffbistro101.com/modules/web/index.php/id/1', None, None, '1592416428', 'http://diamondlifegear.com/', '1592416434', 'https://www.moes.com/find-a-moes/south_carolina/fort_mill/6014?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://lupisfamouspizza.com', None, 'http://anvilbaraz.com', 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store121', None, None, 'http://www.tumi.com/', 'https://stores.guitarcenter.com/las-vegas-lessons?source=4GOA5AJBB', 'http://www.laboilseafood.com/mississaugawest', 'http://www.rfccoaching.com', 'https://www.pizzaville.ca', 'http://automediclasalle.ca', 'http://www.drews-plumbing.com/', 'http://www.mymeritdental.com/locations/dental-centers/macedonia-oh/', None, None, 'http://www.hrrh.on.ca/', 'http://azdollhouse.com/', None, 'http://t7bistro.com', 'http://www.petpro.biz', 'http://www.steeltownfirearms.com', 'http://www.premiereballroom.com/', None, None, 'http://www.harkinstheatres.com', None, 'http://papachevos.com/', None, 'https://desertflowercleaningservices.com', None, 'http://www.balloonswithatwist.com', 'http://www.shillelaghspub.com/signalhill/', 'http://www.courttravel.com', None, 'https://www.discounttire.com/store/az/surprise/s/1504?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280197189&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.mrjimsdealsonwheels.com/', 'http://www.gotquicksrc.com', None, 'http://www.winners.ca', 'https://repartoveloce.com', 'https://getwelloiled.com', None, 'http://www.moonvalleyplumbing.com', None, 'http://efficienthomepro.com', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.web-don.com', 'http://fracshion.com/', 'http://www.myurbanwalk.com', 'https://www.redrockperio.com', 'http://www.silverstatecu.com', None, 'http://www.vetpartnersaz.com', None, 'http://anotherhomefurniture.com', 'http://drewsgarage.us', 'http://www.thecomputerstoppittsburgh.com', 'https://locations.jackinthebox.com/us/az/scottsdale/20385-n-hayden-rd', 'https://www.publicstorage.com/north-carolina/self-storage-matthews-nc/28105-self-storage/892?pid=wyelp&CID=1245&CHID=AFL', 'http://www.hurricanewings.com/', 'http://www.lepainquotidien.com/', None, 'http://paniq.ca/', None, None, 'http://www.stephenlynchhairstudio.com', 'https://bentleyrealtygroup.com', 'https://www.officedepot.com/storelocator/az/scottsdale/officemax-6283/', None, 'http://www.rainbowmedcenter.com', 'http://www.hellotokyolasvegas.com', 'https://bayshorehomesales.com', None, 'https://www.discounttire.com/store/az/fountain-hills/s/1633?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'https://www.stanleysteemer.com/?utm_source=yelp&utm_medium=referral&utm_campaign=yelp_branch_ws_ad', 'https://locations.wendys.com/united-states/oh/richfield/5219-brecksville-rd', 'http://www.magicshoerepairlv.com', None, 'http://www.pbspicks.com', 'http://www.thepriory.com', 'http://www.kentcycle.com', 'http://www.marknelsonphoto.com', 'http://www.functionalfitcharlotte.com', 'https://www.sonoransmile.com/phoenix-orthodontic-office', None, 'http://thebrakeguys.com/', 'https://www.merrymaids.com/west-las-vegas', 'https://simply-laundry.com', 'http://ronsgrillgyros.site', None, 'http://www.MattyHui.com', 'https://overeden.com', 'http://www.depotgibsonmill.com', '1592416774', 'http://www.JimmyJohns.com', None, 'https://pinkboxdoughnuts.com', None, 'https://www.mec.ca/en/stores/calgary', 'http://www.goldennugget.com/LasVegas/spa_services.asp', 'http://www.scottsdalepromenade.com', 'http://www.arizonaqualitypools.com', 'http://northparklounge.com/lawrenceville/', 'http://www.pooleshopcharlotte.com', None, None, 'http://dormontlibrary.org/', 'http://www.karebearplayland.ca/', 'http://charmeck.org/city/charlotte/Airport/Pages/default.aspx', 'http://www.secondcup.com', 'http://alibitheshow.com/', 'http://www.bestevercarpetcleaning.net', 'http://perfexionskin.ca', 'http://www.ihg.com', 'http://www.walkertow.com', None, 'http://deseretbook.com/stores/show/86', 'http://www.earwaxwisconsin.com', 'http://www.miescuelitachildcare.com/', 'http://www.fairportlighthouse.com', 'http://www.jtboxing.com/', None, 'http://www.aztobacco.com/', 'http://operationminidonuts.com', None, 'http://foothillsanimal.org', 'http://www.masscreenprinting.com', None, 'http://www.minimarkham.ca', None, None, 'http://www.rotorooter.com/', 'https://www.nofrills.ca/store-locator/Jim%27s+nofrills+%28Islington+Ave.%29/0753?storeId=0753', 'http://www.arizonagolfcartrepair.com', None, '1592416910', 'http://www.airportinncharlotte.com', 'http://www.Flannys.com', None, 'http://www.ritosbakery.com', 'http://www.bellelaviemedspa.com', None, 'http://sungardenrestaurant.com', 'http://www.liberatidds.com', 'https://www.carries-creations.com', 'https://www.bellagio.com/en/nightlife/petrossian-bar.html', 'http://www.conflictkitchen.org', 'http://israelstransmissionslv.com', 'https://www.valsmobilegrooming.com/', 'http://www.kimberfire.com', 'http://www.thedrakehotel.ca/BBQ', 'http://www.kay.com', 'http://www.westsidesigns.com', None, 'https://salvadorenorestaurant.com', None, 'http://www.jmautoonline.com', 'http://www.burritobandidos.com/', None, 'http://www.charleys.com/', None, 'http://www.aveda.com', 'http://www.idonails.ca/', 'http://fortpittclassiccars.com', '1592417007', None, 'http://www.salon89lv.com/', 'https://skinaddictstudio.com', 'https://nationwidevision.com/locations', None, 'http://mypickapart.com', 'https://az-tattoo-asylum-llc.business.site', 'http://tranquilitymassageaz.com', None, 'https://www.uptowngardensapartments.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://polloinkaexpress.com', None, 'http://www.clevelandmetroparks.com', '1592417059', 'http://www.greyhound.ca', 'http://www.bikeblastlasvegas.com/', 'http://www.locknloadgunstore.com', None, '1592417076', 'https://www.bathandbodyworks.com', 'http://www.cbac.com/avon', 'https://www.americasbest.com/store-list/rocky-river-oh-44126/', 'http://www.pizzaals.com', None, 'http://www.bradgarrettcomedy.com', 'https://www.walmart.com/store/4356/las-vegas-nv/details', 'https://www1.shoppersdrugmart.ca', 'https://www.dinopalmierisalon.com/locations/la-place/', 'https://www.nhlakesidefamilyphysicians.org', 'http://www.farinaccipizza.com/', None, 'http://www.tfiarrowhead.com', 'http://greenlandmoving.com/', 'http://www.wirelesstoyz.com', '1592417125', '1592417129', 'http://www.uwhealth.org/pharmacy/rxrefill/13335', None, 'https://www.bluediamonddentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://dogtropolis.net', 'http://www.truevalue.com/sarasnicks', 'http://www.welchplastics.com', 'http://dogsalldaycharlotte.com', 'http://www.ritters.com', 'http://www.elitenorthscottsdale.com?utm_medium=listing&utm_source=yelp', None, None, 'http://www.bojangles.com', 'http://fiveguys.com/', None, None, 'http://www.mankindgrooming.com/', 'http://www.thesweetgreens.com', 'http://www.pastasandpastry.com/', 'http://www.asui.org/', 'http://ellisparkmedical.com', 'http://www.petrarealtygroup.com', 'https://www.vans.com', 'https://elsupermarkets.com/phx-51st-5127-w-indian-school-rd/', None, None, 'https://connorgroup.com/apartments-charlotte-nc/quarterside/', None, None, 'https://www.alamo.ca/en_US/car-rental/locations/location-details/CA/YYCC74-calgary-10th-ave-wlkp.html?iataNumber=AL022392&affiliateRes=Y&cm_mmc=Yelp-_-Local-_-National-_-null%20%C3%8A', 'http://www.harborfreight.com', 'http://www.yogisgrill.net', 'http://marypreheimgroup.weebly.com', 'https://www.belmontdentistry.com', 'http://www.canyonfallsvegas.com', 'http://meineke.com', 'http://www.shishexpress-yyz.com', 'http://www.marketdistrict.com/Locations/Detail.aspx?LocationID=7', None, 'http://www.scottsdalechiropractic.com/south/', 'http://www.macdonaldortho.com/', 'http://www.thederbypub.com', 'http://adogrefined.com', 'http://www.foothillsrehab.com/', 'http://www.tilerestoration.com', 'http://www.burlingtoncoatfactory.com', 'https://local.pharmacy.safeway.com/az/phoenix/3132-e-camelback-rd.html', None, 'http://www.yumzfrozenyogurt.com/', 'http://www.poolxpertscharlotte.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.truwest.org', None, None, None, 'http://www.aerie.com', 'http://shell.com/', None, 'http://www.dollargeneral.com', 'https://www.storage-solutions.org/self-storage-surprise-az-f3642', None, 'https://centerforsightlv.com', 'http://www.contemporarycalgary.com', 'https://www.supercuts.com/locations/pa/bridgeville/collier-town-square-haircuts-80302.html', 'https://www.nickspizza.biz', 'http://www.chankoshabu.com', 'http://www.hgrinc.com', 'https://www.handy.com/yelp50cc?utm_source=yelp&utm_medium=CPC&utm_campaign=LAS-Handy-Yelp', 'http://www.paddlecharlotte.com', None, None, '1592419469', 'http://www.orbansflowers.net/?Yext=39-4486AA', None, '1592419480', None, 'http://www.bexleyrosedale.com', '1592419491', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLEMD', 'http://hillcrestgolfclub.com/', 'http://www.scottsdaleresortandathleticclub.com', None, 'http://www.peterpiperpizza.com', None, 'http://www.restomirchmasala.com', 'http://www.worldshottestbats.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXMC', 'http://www.walmart.ca', 'http://lasvegasfatlosscenters.com', 'http://carsonstreettattoo.wixsite.com/csts', 'http://www.bayviewhill.ca/', None, 'https://www.yogurtini.com', 'http://www.musicboxcle.com', 'http://marina-dosa-tandoori-grill-westwinds-ne.business.site', 'http://www.pulte.com/communities/az/phoenix/fireside-at-desert-ridge/17670/index1.aspx', 'http://www.koslawn.com', 'https://www.lasikvisioninstitute.com/lasik-eye-surgery/charlotte-surgeon-center/?venid=YLP31&subid=CHA', 'https://www.storquest.com/self-storage/az/tempe/9052', 'http://www.burkesoutlet.com', 'https://www.sunvalleycc.com/tempe/', None, 'https://www.vidabellamedspa.com', 'https://taoacuclinic.com', 'http://www.jameswexler.com', None, 'http://www.indulgencehead2toe.com', None, None, 'http://www.themovementfactory.com', 'http://junipergrill.com', None, 'http://www.petculture.com/', None, None, 'http://boulevard1820.net', 'http://www.pittsburghbraces.com/', 'http://watersandcompanysalon.com', None, None, 'http://www.littlegreenmaidservices.com', 'http://www.lyriclv.com?campaign_code=yelp_Lyric_NV_89183', None, None, 'http://shadysidedentistry.com/', 'http://medinasautorepair.com', 'http://deanohair.com', 'https://www.anylabtestnow.com/franchises/huntersville-28078', 'http://lenasrotianddoubles.ca', None, None, 'https://denises-safe-haven-daycare.business.site', None, 'http://www.purplerainspa.com', '1592419677', 'http://www.accidentloan.com', 'http://www.obsessionsfashion.com', 'http://www.freshmedclt.com', 'http://www.gintermechanical.com', None, None, 'http://www.lakemetroparks.com/select-park/veterans-park.shtml', 'http://www.wvendocrine.com', 'http://rabenglass.com', 'http://thewaterboyaz.com', 'http://cjerkpit.com', 'http://twinriverspropertiessc.com/', None, None, 'http://www.taxwizardsinc.com/', None, 'http://www.dhcmesa.com', 'https://www.mirage.com/en/nightlife.html', 'http://www.freedomofmotion.com', 'http://www.constantinosmarket.com', 'http://www.waldendentistry.com', None, None, 'http://www.tea2go.us', 'http://www.rayknowsvegas.com', 'http://www.livavenida.com', 'http://www.thriftyprincess.ca', 'http://www.garthwilliamscasting.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.rossstores.com', 'http://www.alpinepools.com', 'http://www.modernfarmaz.com', 'http://www.quiktrip.com', 'http://www.drautomotivephx.com', 'http://lasvegas.jiffylube.com/Locations/Store/2668/2583-WINDMILL-PKWY-HENDERSON-NV-89074-5358', 'https://www.caraleavalleyapartments.com', 'https://haircutmenpeterstownshippa.com', 'https://www.sprint.com/storefronts/bd/sprint-charlotte-nc-28273-d-101109/', 'https://www.hihealth.com/hi-health-supermart-baseline-dobson-mesa/', None, 'http://www.costco.ca', 'http://www.cheeseboutique.com', 'http://www.thermotwin.com', None, 'http://royalfurnituregallery.com', None, '1592419828', 'https://www.hihealth.com/hihealth-7th-street-bell-phoenix/', None, 'http://www.kirkdevco.com', 'http://www.accutv.com', None, 'http://twitter.com/#!/chefandfriends', 'http://www.myspace.com/addictedbodyart', 'https://store.vioc.com/nc/indian-trail/13904-independence-blvd-28079-BD0013', 'http://www.vavatoronto.com', 'http://themodernlv.com', 'http://www.mikesquirephoto.net/', 'http://www.cameracompany.com', None, 'http://www.allstarbailbondslv.com', 'http://hannahnailspalasvegas.com', None, 'http://solsticearcadia.com', None, 'http://www.biscuitscafe.com/', 'http://www.therichmondgrill.com/', None, None, 'http://www.thearchpedispa.com', 'http://www.thorps.org/', 'http://learyfamilydentistry.com', 'https://www.chilis.com', 'https://www.petsmart.com/stores/us/az/mesa-store0135.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', None, None, 'http://www.1947tavern.com/', None, 'http://www.brakemasters.com', None, 'http://www.firstfoodandbar.com', 'http://ckjj.com', 'https://www.i17tbirdstorage.com', 'https://www.hansenmortuary.com', 'https://www.ashleyfurniturehomestore.com/furniture-stores/united-states/nv/las-vegas/lasvegas?cmpid=2016YELP', None, 'http://www.nirenandassociates.net', 'http://transmissionfix.com/', None, 'https://www.euphoriahairsalon.net', 'https://k9allure.com/?fbclid=IwAR3aKeuAfCEJDYoitZ2g6yvADgPbQkJKpY32fRdsVzPLql8_Xr8dZwMw9Wg', 'https://ozstudioaz.com', 'http://www.threefiftypgh.com', None, 'http://www.partybusesinlasvegas.com', 'http://www.fuhrmandodge.com/', 'http://www.thecompanystorenoda.com', 'https://maryamscakery.com', 'https://www.rearoadanimalhospital.com', 'http://www.cimdocs.com', None, 'http://www.brooklinpourhouse.com', 'http://www.spooledrotten.net', 'http://davincihs.com', 'http://archesfootinstitute.com', 'http://www.aaronperryagency.com?cmpid=ievm_blm_0006', 'https://www.thebrick.com', 'https://www.craigscookies.com', None, None, 'http://www.scalesntails.com', 'http://www.groundhogpub.com/', None, None, 'http://www.restaurantlesurcouf.com', 'http://smokespoutinerie.com', 'https://local.fedex.com/az/scottsdale/office-2256/', 'https://www.ultimateautolv.com', 'http://fiveguys.com', None, None, '1592420033', 'http://www.purdys.com', '1592420038', 'https://malibuhair.wixsite.com/malibuhairandspa', 'http://www.yoforia.com', 'http://www.hottopic.com', None, 'http://theolivegrill.com/', 'http://www.bk.com', 'http://www.frankandtonysplace.com/', 'http://www.bathandbodyworks.com', 'http://www.brow-smith.com', None, 'http://www.protectyourhome.com/dir/yelp', None, 'http://www.wildtaurus.ca', 'http://www.lvclean.ca', 'http://www.papajohns.com/', 'http://www.bolerocalgary.com/', 'http://100degreeshotpot.com/', 'https://www.batteriesplus.com/store-locator/sc/rockhill/batteries-plus-422?utm_source=yelp&utm_medium=local&storecode=422', None, 'http://www.adesa.com/LasVegas', 'http://ribnroll.com', None, 'http://www.GeorgetownVW.com', 'http://www.showermewithlove.com', None, 'http://www.greaterclevelandaquarium.com/', 'http://www.towpathcu.com', None, 'http://www.superdutyshop.com', 'http://terraandmare.com', 'http://www.changjiangsp.com', 'http://stores.bestbuy.com/az/goodyear/1408-north-litchfield-road-485.html', 'http://www.littlecaesars.com', 'http://www.duq.edu', None, 'http://www.drpapandreas.com/', 'http://www.goodsenses.com', '1592420128', 'https://infinitehealingcenter.com', 'http://www.lululemon.com/scottsdale/scottsdaleshowroom', 'http://www.theweddingcakeshoppe.com', 'http://www.tiptonorthodontics.com/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', '1592420144', '1592420146', 'http://www.outback.com/locations/nv/las-vegas-craig', 'https://mojavepestcontrol.com', None, 'http://www.bikkuri.ca', None, None, None, 'http://leesliquorlv.com/locations/lake-mead-tenaya-2/', 'http://www.digital-one.com', 'https://www.listenandcare.com', 'http://www.raphaelsbeautyschool.com', None, None, '1592420177', 'http://afivegas.com', 'http://www.smallhandsbigart.com', 'http://www.spicnspancleanings.com', 'http://www.fitchicks.ca/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1015+East+Ray+Road-Chandler-AZ-85225/storeid=7849?cid=ps_ylp_2020', None, 'https://www.mk3firearms.com', 'http://babavegan.com', 'http://www.science.discoveryplace.org', 'http://www.europizzacafe.com/', None, None, 'http://www.joybistro.com', 'http://www.gardenspath.com', 'https://www.collegenanniesandtutors.com/lasvegasnv/', 'http://www.torontopubliclibrary.ca', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEAK', None, 'http://www.revivalapts.com', 'https://www.enterprise.com/en/car-rental/locations/us/az/downtown-chandler-5008.html?mcid=iyp:8368400', '1592420230', None, 'http://www.f-lhomeimprovements.com', None, 'http://www.barberswest.com', 'https://www.lasvegasnevada.gov/portal/faces/wcnav_externalId/pf-floyd-lamb?_afrWindowId=null&_afrLoop=1180975913218031&_afrWindowMode=0#%40%3F_afrWindowId%3Dnull%26_afrLoop%3D1180975913218031%26_afrWindowMode%3D0%26_adf.ctrl-state%3D8yz0uorum_4', None, None, 'https://scottsdalebarber.com', 'http://www.littlelakewoodpasta.com', 'http://www.gilbertsquareapts.com', None, None, 'http://www.poolcleaninghenderson.com/', 'http://www.trlawing.com', '1592420267', None, 'http://spreadthewordnevada.org/', 'http://www.cashamerica.com/SUPERPAWN-stores/AZ/PHOENIX/Pho09', None, 'http://www.dominos.com', 'http://www.gordmans.com', 'http://www.bloomlasvegas.com?campaign_code=yelp_Bloom_NV_89129', 'http://theupsstore.ca/148', 'http://joechicago.ca/fr', 'http://theexchange.com', 'http://www.scvdg.com', None, None, 'http://www.Kaizensushi.ca', 'http://www.kmhlabs.com', 'http://www.stylegarage.com', None, None, 'http://www.thrifty.com', 'http://www.sagewoodapartments.com', None, 'http://buildingmanagerchandler.com', 'http://philistinetoronto.com/', 'http://www.seafrontfishmarket.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://www.motherhood.com/maternity-stores/nevada-henderson.asp', 'http://www.eatpizzapalermo.com/', 'https://tsautoglass.com', 'http://www.partypeoplerentals.com', 'http://www.peets.com/?cm_mmc=yelp*peets*8_28_12_homepage*na', 'http://www.acmepilates.com', 'https://www.zaxbys.com/locations/sc/fort-mill/3401-hwy-21/', 'http://www.papadschampaign.com', 'http://www.fsliquidators.com', 'http://www.dairyqueen.com', 'http://www.ryanzhu.realtor', 'https://www.theregencyapts.net', 'http://www.pelicanospizza.com/', None, 'https://carylbakervisage.com/pages/erin-mills-town-centre', 'http://www.homedepot.ca', None, None, None, 'http://www.extendedstayamerica.com', 'http://www.maricopa.gov/pets', 'http://www.centurylink.com', None, None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Tempe-AZ-85284/723047/', 'http://www.cauldronicecream.com', 'http://www.alshvac.org', None, 'http://www.PhototherapyExperts.com', 'http://www.goleeyeworks.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360246&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://avis.com', 'http://www.TotalLifeAZ.com', None, 'http://www.nucleus.com', 'https://www.walmart.com/store/5768/tempe-az/details', None, None, 'http://opus1ortho.com', 'https://www.robertcohenmd.com/our-surgeons/dr-sigalove/', 'http://www.westcoasttattooparlor.com', 'http://www.puffandfluffspa.com/uptown/', 'http://www.thecoreinstitute.com', 'http://www.patrickliudds.com/', 'http://limestonemotorcars.com', None, None, None, 'http://www.lesslieanimalhospital.com', 'http://www.sunridgenissan.com', 'https://sugar-roll-ice-cream.business.site', None, None, 'http://www.pulcinellatoronto.com', 'https://www.indigopgh.com/dine.htm', None, 'http://icolornailbar.wixsite.com/website', 'http://www.southpointechiropractic.com', 'http://www.alphagraphics.com/centers/mesa-arizona-us291/', None, 'http://www.rozbodyfit.com', 'https://www.take5oilchange.com/locations/oh/mayfieldheights-130/', 'http://unlimitedblue.ca', 'https://www.aappleblossom.com', 'http://desertflying.club', 'http://www.thedogmarket.ca', 'http://www.shopslateinteriors.com', None, None, None, None, None, 'http://www.americanpridemobiledetailing.com', 'http://www.storybookentertainmentaz.com', 'http://www.greeneconcreteleveling.com', 'https://www.palmglenanimalhospital.com/?utm_source=yelp&utm_medium=social', None, None, 'http://spiritedcyclist.com/', 'https://www.wyndhamhotels.com/hotel/03766?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:03766', 'http://www.kingsinn.net', 'https://www.westelm.com/?cm_ven=yelp&cm_pla=yelp&cm_ite=876', 'https://solblooms.com', None, 'http://forgottentaste.com/', 'http://www.wildfigcatering.com', None, 'https://aclasvegas.com', None, 'http://www.eyemasters.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.caferio.com/locations/eastern', 'http://www.eastsidekia.ca', 'http://www.bodyworkatwork.com', None, None, 'http://www.stjoanofarc.com', 'http://www.saturdaydinette.com/', 'http://www.goldeenmfr.com', 'http://www.truckrepairlasvegas.com', None, 'http://www.firstmarkhamrehab.com', None, 'http://www.banasstones.com/', 'http://www.citybakeryaz.com', 'http://www.inplayinc.ca', 'http://www.revivenailson.com', None, 'http://www.zara.com', None, 'http://www.softenerserviceaz.com', None, 'https://callorange.com/locations/locksmith-peoria-az/?utm_source=yelp&utm_medium=yelp', 'http://www.cmlibrary.org/locations/branches.asp?id=10', '1592420749', 'http://www.tgifridays.com', None, None, None, 'https://www.andresbistroandbar.com', None, 'https://www.affordablewindowsofaz.com', None, 'http://gotstyle.ca', 'https://www.autoglassrepair-pittsburghpa.com', 'https://br.coffee', 'https://www.caesars.com/rio-las-vegas/things-to-do/masquerade-bar?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=MasqueradeBar&utm_content=bar', None, None, 'http://www.toronto-employmentlawyer.com', 'https://casemogulphonerepairs.com', None, None, None, None, 'http://saajgrill.com', 'http://www.leaderofthepackdoggiedaycare.com', None, 'http://animalhospitalfairview.com', 'http://www.dunkindonuts.com', 'http://www.absolutesalonaz.com/', None, '1592420838', 'http://www.goodcheese.ca', 'http://www.jasminespa.org', 'http://americaninnaz.com', 'https://www.avanariverranch.com', 'http://www.LasWagesNV.com', 'https://www.batteriesplus.com/store-locator/wi/glendale/batteries-plus-541?utm_source=yelp&utm_medium=local&storecode=541', 'http://www.tomclarkchevy.com/?cs:pro=repman&cs:e=yelp', None, None, None, None, 'http://www.bk.com', 'http://www.densleydental.com', 'http://newoutlookopticalnv.com', None, 'http://www.europeanskincare.com', 'https://www.maid4condos.com', None, 'http://www.hgcabinetsdirect.com/', 'http://crestbakery.net/', 'http://fbihvac.com/', None, 'http://salondiva.ca', 'http://prioritypethospital.com/', '1592420923', 'https://www.publicstorage.com/arizona/self-storage-phoenix-az/85027-self-storage/1113?pid=wyelp&CID=1245&CHID=AFL', None, None, 'http://pitapitusa.com', 'https://ayalasmobiledetailllc.godaddysites.com', None, None, None, 'http://www.blacktheatretroupe.org', 'http://www.pfaffaudi.com', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'https://www.jasonsdeli.com/restaurants/woodlawn-deli', 'http://www.azpremierpass.com', None, 'http://www.sincitysnoballs.com', 'https://petvalu.com/location/2044', 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', 'http://www.aonemovers.com', None, 'http://www.langmotorcar.com', None, 'http://www.fixt.ca', 'http://lasvegaspondcare.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FLASGR', None, 'http://www.lebigoudi.ca', None, 'http://www.betseyjohnson.com', 'http://www.ymcacharlotte.org/harrisexpress', 'http://www.lssecurity.com/', 'http://rwmechanicalvegas.com/', 'http://eathealthyeatgreek.com/locations/paradise-valley/', 'http://www.blondiesbailbondslv.com', 'http://www.michaelscollision.com', 'http://www.purogelato.com', 'http://www.jmjautoservice.com', 'http://www.eggsmart.ca', 'https://www.freewayinsurance.com/office-locator/freeway-insurance-mesa-az-85210', 'http://www.fuzen.ca', 'http://robertostacoshop.com', None, 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'https://www.tomshouseofpizza.com', 'https://www.dandlchandlerglassworks.com', 'http://www.itstheicingonthecake.ca/', 'https://www.psncenergy.com/', 'https://www.sprouts.com/stores/details/-/store-details/view/store/501/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://www.pokewrap.com', None, 'http://www.jimyzautomotive.com', 'http://www.tricityaudiology.com', 'http://www.buyncell.ca', None, 'http://69vintage.com/', None, 'http://www.petvalu.com', 'http://www.nataraj.ca/', None, 'https://www.applewoodauto.com', 'http://www.dynastyautogroup.com', 'https://www.metrotoyota.com', None, 'http://www.farmersfitness.com', None, 'http://www.undergroundgarage.ca/', 'http://www.behindthemask.com/', None, 'http://www.shoelessjoes.ca', 'https://7to7eatery.com', None, None, None, None, 'http://thehilltopbarbershop.com', '1592421177', 'http://www.georgetownkia.com', 'https://studios.frenchiesnails.com/southhills-pa', None, 'http://www.joltajava.com/', 'http://www.thenakedtart.com', 'http://fuelplus.ca', None, 'https://windowinstallationpittsburgh.com', 'http://www.lvsewingmachine.com', 'http://www.rousemgmt.com/hawks-landing', 'http://www.1stpetvet.com/chandler', 'https://www.starbucks.com/store-locator/store/17761', None, 'http://www.notredamebh.com', None, 'http://www.amici.catering', 'http://www.pristinedentalaz.com', None, 'http://www.cleanfreakcarwash.com', None, None, None, None, 'http://sites.google.com/site/natesbarbershop1', 'http://chiropractictherapyhenderson.com', None, 'http://www.tingalls.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.wimpysparadise.com', 'http://www.pizzanova.com/', None, None, 'http://www.ahuntdesign.com', None, 'http://www.elkinsautomotive.com', 'http://www.phoenix.hyatt.com', None, 'http://arizonafoodtours.com', None, 'http://theastoratosborn.com/?utm_medium=listing&utm_source=Yelp', 'https://www.ttc.ca/Subway/Stations/Sheppard-Yonge/station.jsp', 'https://locations.wendys.com/canada/on/etobicoke/5250-dundas-street-west', 'https://fencesdelsol.com', 'https://www.clearly.ca/stores/queen-west-store', 'http://hundredflowerswillowick.com', None, None, None, None, None, 'http://ljicollisioncenter.com', None, None, None, 'http://mandf4less.wix.com/mattess4less', 'http://www.horseshoecleveland.com', 'https://www.signaturestyle.com/locations/on/toronto/first-choice-haircutters-5677.html', 'http://www.lalingerieshop.com', 'http://www.bk.com', 'https://www.menswearhouse.com/store-locator/2405?utm_source=yelp&utm_medium=listing&utm_content=2405&utm_campaign=NV', 'http://www.stjeanpizz.com', None, 'https://a1wildlifecontrol.net', 'http://www.ThoseCallaways.com', 'http://www.xclusivevegaslimos.com', None, 'http://www.mydcdental.com', None, 'http://www.muranocleveland.com', 'http://www.learnedowl.com', 'http://c-dsilver.com', 'http://www.nickstaphouse.com', 'http://luisautorepairphoenix.com', '1592421417', 'https://www.marcos.com/locations/az/surprise/w-waddell-rd-suite-103?s=true', None, 'https://www.jiffylube.com/locations/az/chandler/2649', 'https://www.hilton.com/en/hotels/lassrhx-hampton-suites-las-vegas-south/?SEO_id=YELP-HP-LASSRHX', None, None, 'http://www.publichouselv.com', 'http://www.pennsylvaniaappraisers.com', 'http://thepalaceaz.com', 'https://www.urbanmedspacharlotte.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://favourdelivery.ca/', 'http://www.kineticperformancecenter.ca/', 'http://www.mercyfitaz.com', 'http://www.baskinrobbins.com', 'http://langleyscountrymarket.com/', 'https://www.jpermanentmakeup.com', 'http://www.goodfellascigarlounge.com', None, 'http://donnellygroup.ca/walrus/', None, 'http://www.costco.com/warehouse-locations/warehouse-674.html', 'http://www.westwinddriveins.com/westwind/index.php?r=drivein/location&idtheater=3999', 'http://todayshomeinc.com', 'http://www.paradisevalleyvets.com', 'https://www.fieldofdreamscenter.com/baxter//?utm_source=Yelp', None, None, 'https://www.billyjacksshack.com/locations/noda-charlotte-nc/', None, 'http://www.endsclothing.com/', 'https://locations.einsteinbros.com/oh/chagrin-falls/54-shopping-plz.html?utm_source=storelocator', None, '1592421526', None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, None, 'https://www.fastmed.com/urgent-care-centers/tolleson-az-walk-in-clinic-lower-buckeye-road/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', None, 'https://www.esso.ca/en/gas-station/mississauga-on-erinmillscreditvalley-200302504', 'http://mandaraspa.ca', 'http://airparkautospa.com/', 'http://www.allarizonaautoparts.com/', 'http://www.pitapitusa.com', 'http://www.elysianatsouthernHighlands.com', None, 'http://www.laserhealthsolutions.com', 'http://www.jaburgwilk.com', None, 'http://www.distefanos.com/', None, None, 'http://www.floydskitchen.com', 'http://www.spaofuro.com', None, None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/2672+Blanding+Boulevard-Middleburg-FL-32068/storeid=4344?cid=ps_ylp_2020', 'http://www.indochino.com', None, None, None, '1592421626', 'https://FlairTradeConsign.com', '1592421633', '1592421636', 'http://www.dragon-buffet.com', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'https://locations.wendys.com/united-states/pa/moon-twp/8703-university-blvd.', 'http://montgomeryautobodyandpaint.ca', 'https://www.tropicaltreasuresphoenix.com', None, None, 'http://www.BuiltByBraden.com', 'http://www.samstownlv.com/shop/gatsbys-salon?disid=wmm_yelp_st_corporate_gatsbyssalon_organiclink', 'http://algebrateahouse.com', '1592421678', None, None, 'http://www.thestillfinespirits.com', 'http://www.salvatorepuccini.com', 'http://fixauto.com/mississauga-central', 'http://www.cornishpastyco.com', 'http://www.letsdolunchaz.com', 'https://www.trulynolen.com/location/arizona/tempe-pest-control?utm_source=yelp&utm_medium=listing&utm_campaign=', 'https://pellawi.com', None, None, '1592421715', None, 'http://www.able-electriclv.com', None, None, 'http://fitness.reebok.com/store-locator/', 'http://www.greatclips.com', 'http://rescueoneair.com', 'http://www.thekakori.ca', 'https://www.walmart.com/store/1839/lorain-oh/details', 'http://www.parkroadshoppingcenter.com', 'https://www.lumberliquidators.com/ll/stores/wi/sun-prairie/2255-mccoy-road?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1104', 'http://hungrymonkaz.com/', None, '1592421759', None, 'http://www.hallofframes.com', 'http://discounttirecity.com', None, None, 'http://www.desertstarfp.com', 'http://www.lapetite.com/your-local-school/charlotte-nc-7469/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', '1592421784', None, 'https://www.biggby.com', 'http://www.mesacomics.com/', 'http://www.castlehonda.ca', 'http://www.mattressdepotaz.com', 'http://www.herballygrounded.com', 'http://mixfitphoenix.com', None, 'http://www.multipure.com/', None, 'https://ehhardware.com', 'http://www.arizonamicrogreens.com/', '1592421826', 'https://www.fivestarlimonv.com', '1592421833', None, 'http://granitesolutionsaz.com', 'http://www.calgarypodiatrist.com', None, None, 'http://www6.rentacenter.com', 'https://www.sprint.com/storefronts/bd/sprint-strongsville-oh-44136-d-4688/', '1592421858', 'https://www.augustinaboutiques.com', '1592421863', 'https://www.academytutorsonline.com', 'https://www.chapmanfordaz.com', 'http://www.freaklingbros.com', 'http://www.pizzabellagio.com/', 'http://www.bk.com', 'http://www.york-dental.com/', 'http://www.phoenixnailsspa.com', 'http://www.starbucks.com/store/14175/', 'http://www.disn-lv.com', None, None, 'http://www.watchlink.com', 'http://www.ChristieStark.com', 'http://www.jiffylube.com', 'http://www.goodyhouse.com', 'http://www.desertparkway.com', 'http://www.cannondeli.com/', None, None, None, 'http://www.mrglassworks.com/locations/arizona/surprise-windshield-replacement/', 'http://www.GarbageGoodGuys.com', None, None, 'http://popeyeschicken.ca', 'http://www.petco.com', '1592421951', 'http://www.farnham-alelager.com/', None, 'http://www.mikehammershow.com', 'http://www.CAACentre.com', None, None, None, None, 'http://southwestfootinstitute.com', None, None, 'http://www.coffeebean.com', None, 'https://www.staples.com', None, None, 'https://www.davescosmicsubs.com/locations/hudson-ohio', 'http://scottsdalegi.com', 'http://www.nationaltestingnetwork.com', 'http://chevron.com/', 'http://www.mark-taylor.com/arizona/the-emerson/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.rotorooter.com/ca/alberta/calgary', 'http://www.getprocare.com', 'https://thaiexpress.ca', '1592422037', 'http://ahipoki.com', None, 'http://www.lhmrealty.com', 'https://www.lifeway.com/en/store-detail-4825', None, 'http://freshco.com/stores/bloor-dundas', None, 'https://miapasta.com', 'http://www.azontherocks.com', 'http://www.humptys.com', None, 'https://www.cox.com/local/residential/stores/az/tempe/2040-east-rio-salado-pkwy?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q35', 'https://www.smartstyle.com/en-us/locations/pa/west-mifflin/located-inside-walmart-2281-haircuts-11347.html', 'https://www.walmart.com/store/3354/henderson-nv/whats-new', None, 'http://www.phillipsheating.com', 'http://www.giuseppesanthem.com', 'http://www.bk.com', 'http://www.spoonwoodbrewing.com/', 'http://copainsgourmands.com', None, 'http://www.letsplaydodgeball.com/', 'http://www.quantumspirits.com', 'http://www.ibrowthread.com', None, 'http://www.caledonscurry.ca', 'http://www.avancybridal.com', None, 'http://www.osmri.com', 'http://wellcoffeeaz.com', 'https://www.holtrenfrew.com/en/services/restaurants/holts-cafe/yorkdale', None, 'http://www.gamestop.com/store/us/az/scottsdale/2760/sonoran-village-gamestop', 'http://www.raftingmontreal.com', None, None, 'https://www.westbrookmall.com', 'http://www.sassyspa.net/contact.htm', 'http://www.dwellinspectaz.com', None, 'http://restaurantlasignorina.com', '1592422176', None, None, 'http://www.phoenixfencesupplier.com/', 'http://holisticlactation.com', 'http://www.madisoncomedy.com', None, None, 'https://workoutanytime.com/indian-trail/', 'https://www.anytimefitness.com/gyms/691/Waunakee-WI-53597/?utm_source=yelp&utm_medium=local', 'http://www.getupandgomakeup.com', 'http://www.weed-pro.com/', None, None, 'https://www.staples.com', None, 'http://www.thebumperpros.com', 'https://www.bumperdoctempe.com', 'http://www.yogasource.ca/', 'http://www.ilm-llc.com', None, 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'https://dentaldepotarizona.com', 'http://www.rivierahotel.com/entertainment_ice.asp', 'http://www.pittsburghparking.com/shadyside-garage', 'http://www.geromes.com', '1592422254', 'http://www.securitytitle.com', None, 'http://www.tatumhighlandsdentistry.com/', '1592422266', None, 'https://www.hungryhowies.com/store/hungry-howies-00639?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=639&utm_content=Website_Link', 'https://ymcagta.org/find-a-y/markham-ymca-blvd-rudy-bratty-ymca-centre', 'http://www.burdicklawnv.com', 'http://www.uttonphotography.com', 'https://www.intrusionpest.com', 'https://rsgmusic.com', 'http://www.galaxypilates.com/', 'http://www.azmotocity.com', 'http://storit-lasvegas.com', 'http://www.wix.com/madalynscoffeeandtea/home1', None, 'http://www.lukefamilyhomes.com/', None, None, 'http://www.frysfood.com', None, 'http://AtHomeFitness.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.christchurchphoenix.org/', 'http://www.cactusjoeslasvegas.com/', None, 'http://adamsglassaz.com', 'http://www.sprint.com', 'http://www.madisonchocolate.com', 'http://www.fatburgercanada.com', '1592422350', None, None, '1592422359', None, 'https://assuredauto.ca/locations/toronto-king-west-on', 'http://www.salonrockscottsdale.com', None, None, None, 'http://www.theplatinumhotel.com/dining/dining.asp', 'https://rampaintingllc.com', 'http://stores.fossil.com/nv/las-vegas/fashion-show-8218', 'http://www.brunswickmazda.com', None, 'http://www.wlasvegas.com/?EM=EM_YELP_STWD_LISTINGS_WH_4429_NAD_FM&SWAQ=953P', 'https://www.applebees.com/en/restaurants-willoughby-oh/35055-maple-grove-rd-77041', 'http://www.comfortspamassage.com', 'http://www.tannersbistro.com/#!contact/c24vq', 'http://bikesonwheels.ca', 'https://www.pcapreschool.com/schools/goodyear-az-estrella-mountain-preschool/?utm_source=yelp&utm_medium=local_listing&utm_campaign=yelp_website&cad_campaign=yelp_website', 'http://www.kirklands.com/?cid=pfprn&utm_source=platformpartner&utm_medium=listing&utm_term=366&utm_campaign=az', 'http://www.rivermenbrewingcompany.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.homedepot.com/l/Kannapolis/NC/Kannapolis/28083/3607?cm_mmc=seo-yelp&', 'http://www.theshadysidemarket.com', None, 'http://www.petvalu.com', None, 'http://golfdomemississauga.com/', None, None, None, 'http://www.broadviewpetmedicalcenter.com', '1592422458', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXGP', 'http://oaxaquenarest.com/', None, 'https://seahawksecurity.com', 'http://www.via-pilates.com', 'http://www.arbys.com', None, 'http://www.carpetcapitolflooring.com/', 'http://az.goodyear.charmingcharlie.com/fashion_accessories_goodyear_az_228.html', 'http://www.chatime.com', 'https://www.abbioccorestaurant.com', None, 'http://papajohns.com', 'http://www.julesthedoula.com', None, 'http://jkurleymd.com', 'https://www.eatnpark.com', 'http://www.vegasvaporemporium.com/', '1592422516', 'http://www.kingcrust.com', 'http://www.1hautedog.com', 'http://www.jewarts.com', None, '1592422530', 'http://carlislesbridal.com', 'http://freedomcleaningservicesaz.com/', None, None, None, '1592422550', None, 'http://opalifegreek.com', 'http://moddentistry.com', '1592422564', 'http://www.waxhawvision.com', None, 'http://www.michaelkors.com/', None, 'https://locations.jackinthebox.com/us/az/mesa/525-n-stapley-dr', 'https://www.chick-fil-a.com/scottsdale101', None, 'http://www.aldi.com', 'https://www.rockymountainflatbread.ca/locations/calgary/', 'https://local.pharmacy.safeway.com/az/phoenix/3132-e-camelback-rd.html', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'https://www.wyndhamhotels.com/hotel/11662?tel=18006817991&iata=00093785&cid=fe:ra:20170223:yl:pp:ramca:11662', 'http://lidas-tires-wheels.business.site', 'https://www.dbmassage.com/massage/', 'http://www.stephencooley.com', 'http://www.bk.com', 'http://storelocator.pepboys.com/pepboys/stores/las_vegas/east_charleston/00685', 'http://www.papajohns.com', None, 'http://www.whitewillowdental.com', 'https://www.aspendental.com/dentist/tn/madison/2153-gallatin-pike-n?utm_source=yelp&utm_medium=lociqyext&utm_campaign=Madison%2CTN%28Nashville%29%7C%7CNashvil_TN%7C%7C1469&utm_content=listing', None, 'http://www.boosterjuice.com/', None, 'https://www.shultsfordsouth.com', 'http://www.manzopizza.com', 'https://gtapainstressclinic.com', 'http://mytuscanyvillage.com/myLaVitaTuscana.html', 'https://www.mattressfirm.com/stores/nc/matthews/mattress-stores-matthews-nc-28105-6950.html', 'http://www.rejuvent.com/', 'http://www.sorso.ca', 'https://www.livecosmopolitan.com/?utm_source=yelp', 'http://www.susanpaulhair.net', 'http://www.highpeakswater.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.deervalleyplumbing.com', None, None, 'http://playgroundparma.com', None, 'http://kidsstartpreschool.com', 'http://www.7-eleven.com/?yelp=35850', None, None, 'http://www.fremontcasino.com/dine/paradise-buffet-and-cafe?disid=wmm_yelp_fr_corporate_paradice_organiclink', 'http://www.leonebuilders.us', None, None, None, None, None, 'http://premierpropertyserviceslv.com', None, 'https://stores.joann.com/az/mesa/1305/', 'http://www.sonicdrivein.com/', None, 'http://perfectedgelandscape.com', None, 'http://classicmouldinglv.com/', 'http://www.butchersofdistinction.ca', 'http://www.tallentspeechtherapy.com', 'http://glendaleazbeautysalon.com', 'http://www.cigna.com/cmgaz/locations/tempe-medical-office', 'http://stagecoachlocksmiths.com', 'http://stonepizzeria.com', 'http://www.doughboys412.com', 'http://www.leightonagency.com', None, 'http://www.bigbenpub.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.chick-fil-a.com/beachwoodplacemall', 'https://www.dogtopia.com/scottsdale-raintree/', 'http://www.vcalderonlaw.com', 'https://www.allurevegas.com', 'https://www.avantigreen.com', None, None, '1592422821', 'http://www.SmokeysBarbeque.com', None, 'http://www.kuljitindia.com', 'http://www.capsuletoronto.com', None, 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', None, 'https://apclasvegas.com', 'http://www.sportsconnectionnc.com/location_detail.php', 'https://www.dairyqueen.com/us-en/locator/Detail/2398', 'http://www.santanfurnitureaz.com/', 'http://appliancerepairphoenixaz-16st.ara-repair.com', 'http://cbnsalon.com', 'http://www.blueroothealth.com', 'https://www.theaftermidnightgroup.com/wisconsin', 'https://www.themissionaz.com', None, None, 'http://www.mykidzdentist.com', 'http://www.starbucks.com', 'http://www.thecapitoleventtheatre.com', 'http://cardinalcu.com/', 'http://www.gsilasvegas.com', None, None, 'http://www.jademonkeybar.com', None, 'http://www.audiovideochoices.com', 'https://www.baierlacura.com', 'http://charlotteshairstudio.net/services/', 'http://www.glitteringlightslasvegas.com', '1592422933', 'http://www.desertvalleypediatricslv.com', None, None, None, 'http://joesice.com/', 'https://www.noodlebarphx.com', 'http://www.empiremusiconline.com', 'http://www.originaldonnelly.com', 'http://www.greatclips.com/salons/3063', None, 'http://lifewell.us', 'http://clickserve.dartsearch.net/link/click?lid=43700044282956305&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.southtreeservice.com', 'http://www.moes.com', 'http://www.cti-industrialsupply.com', 'http://www.onagertowing.com', 'https://www.harbourfrontcentre.com/shop/index.cfm', 'http://www.arizonahairco.com/', 'https://locations.jackinthebox.com/us/az/mesa/525-n-stapley-dr', 'https://www.middlejamesbrewing.com', 'http://www.trilliumhealthcentre.org', 'http://www.donsglass.com', 'https://locations.wendys.com/united-states/az/gilbert/929-n.-arizona-avenue', 'https://www.ghandilaw.com', 'http://www.borders.com', 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', 'http://www.balancechimassage.com', 'http://www.babiesrus.com', None, 'https://www.campusmobilesolutions.com', None, 'http://www.lucyliterna.com', 'http://copperkettleaz.com', None, 'http://www.totalpoolrestoration.com', None, None, 'http://www.actionpm.com', 'http://pastorcleaning.com', None, 'https://www.walmart.com/store/5387/middlefield-oh/whats-new', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.gaetanoslasvegas.com/', None, 'http://www.BethelBakery.com', 'http://www.kirklands.com', 'http://www.timhortons.com', 'http://www.bikemastersaz.com', None, 'http://www.bigtwomitsubishi.com', 'http://www.rebeloil.com', None, 'http://www.flosdiner.ca/', None, None, 'http://mydance101.com', None, 'http://restaurantmammas.com', 'http://fortmill.dentalworks.com', 'http://bakersfieldtacos.com', 'https://www.panerabread.com/en-us/home.html', None, 'http://www.alliancehomeloans.com/', 'http://www.mydentalnation.com', 'http://www.papa.org/', 'http://www.kimpovietnamese.com/index.php', 'http://www.tarenlenea.com', None, 'https://www.selectphysicaltherapy.com/contact/find-a-location/nc/denver/denver/?ty=xt', '1592424247', 'http://www.osteria.ca', 'http://nettleships.com', 'http://www.payblackwell.com', 'http://www.escapein60.co', 'https://copperstillmoonshinegrill.com', 'http://hardsurfaceslv.com/', 'https://www.bandbloan.com/', 'http://www.highstreetaz.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://captain6lv.business.site', None, None, 'https://dulceriacolmena.com', 'http://www.arbys.com/', 'http://charliessalonspa.com', None, 'https://goodtimeiii.com/site/', 'http://www.motel6.com', 'http://www.swisschalet.com', '1592424314', '1592424317', '1592424322', 'https://www.mynycb.com', 'http://www.timhortons.com/', None, None, 'http://www.blindwholesaler.com', '1592424342', 'https://www.caesars.com/flamingo-las-vegas/things-to-do/the-garden-bar?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=GardenBar&utm_content=bar', 'http://www.kegsteakhouse.com/en/locations/ON/richmond-hill/richmond-hill-keg/', None, None, None, 'http://alohaislandgrill.com/', 'https://mountainsidefitness.com/locations/scottsdale-shea/', None, None, None, None, None, 'http://www.themilkshakefactory.com', None, 'http://www.chateaupooch.net', 'http://driftwoodrestaurantsandcatering.com/', 'http://www.sundevilauto.com/locations/az/glendale/glendale-7', 'http://www.health-reflexology.com', 'https://limoncellolv.com', 'http://www.arcpsychiatry.com', 'http://www.azcrowncenter.com', 'http://www.royalboardshop.com/', None, 'http://www.zapatasrestaurant.com', 'http://Philsautoglass.com', '1592424429', 'http://tabularasaclothing.com/', 'http://www.lasvegasnevada.gov/Find/21174.htm', 'http://www.lightgroup.com/nightlife/jet-nightclub-las-vegas', 'http://www.wiener-shop.com', 'https://www.vibstudio.com', 'http://www.7hillshandcarwash.com', 'http://www.ncdot.org/dmv/', 'http://locations.michaels.com/PA/MUNHALL/1581/', 'http://www.adhaz.com/', 'http://www.spfloorspgh.com', 'http://purecolorbar.com', 'http://diamondsalonvegas.com', None, '1592424480', 'http://www.blue-ribbonk9.com', 'https://www.harveys.ca', 'http://www.thehottspotextremewellness.com', 'http://www.thriftyslasvegas.com/', 'http://www.padivorce.com/', None, None, None, 'http://www.terzettohair.com', None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=2125&localechange=1', 'http://futurebarbershop.com', 'http://www.lakesidepoolsandspasaz.com', 'https://www.greulichs.com', None, 'http://Sheesha.ca', 'http://www.americanfreight.com/?utm_source=yelp&utm_medium=social&utm_campaign=profile', 'https://reptilia.org', 'http://www.penzeys.com', 'http://internationalengines.business.site', 'https://bluewaterpoolservicelv.com', 'http://nails88shop1.com', 'http://www.provisionspest.com', None, '1592424542', '1592424546', 'http://www.einsteinbros.com/locations/3557', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.childtime.com/your-local-school/mesa-az-1436/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://www.unclesamssubs.com/', 'http://www.dunkindonuts.com', 'https://www.olivegarden.com/locations/az/mesa/southern-fiesta-mall-west-mesa-alma-school-rd/1661?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:mesa-az-1661_pl:locurl_rd:1517', None, None, 'https://www.stanleysteemer.com/location-details/Peoria-IL/558', 'http://www.gamestop.com', 'http://robertostacoshop.com', None, None, 'https://www.wellsfargo.com', 'http://www.lecosauto.ca', 'http://www.dunkindonuts.com', 'https://www.bankofamerica.com', None, None, 'https://thaiexpress.ca/locations/', 'http://www.starbucks.com/store/8054/', 'http://www.destingo.ca/', 'https://cortland.com/apartments/attiva-valley-view/', 'http://missbehavegameshow.com', 'https://www.tutoringclub.com/northlasvegasnv/', None, 'http://buildingresourcelimited.com/', None, '1592424621', 'http://www.lasermedsolutions.com', None, None, None, 'http://www.gnawoodworks.com', None, None, 'http://www.caniglia.com', None, 'http://www.muchoburrito.com', None, None, None, 'http://lushusa.com', 'http://www.costco.com', 'http://www.hmv.ca/', 'http://www.villagebakeshop.ca/', 'http://www.transtyle.com/', '1592424668', None, 'http://www.kerrygulino.com?cmpid=R6RO_BLM_0006', None, 'http://www.dollartree.com', 'http://www.thebasilbox.com', 'http://wrapsonthego.catering', None, '1592424684', None, 'http://alcoparking.com/lot-garage/fifteenth-and-smallman-lot/', 'http://www.mydentistaz.com/', 'http://thehairstandard.com', 'http://prettyqnailssurprise.com', 'http://www.nuwunorth.com', 'http://www.ontheskinny.com/', 'http://www.ohms2vapor.com', 'http://cosmedixmd.com', None, None, 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=156&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-156', 'http://www.customfloorsaz.com', 'https://www.archerdental.ca/locations/babypoint/', '1592424720', 'https://rustycarrentals.business.site', 'https://www.aplin.com', None, 'http://www.concentra.com', 'http://www.cutthroatbarbershoppe.com', 'https://www.biondilincoln.net', 'http://www.azstorage.com', '1592424740', None, 'http://www.ivorythailand.com', 'http://heavenlyhookahlounge.com/', 'http://www.greatclips.com/', 'https://www.goldencorral.com/locations/2545/golden-corral-west-thomas-road', 'https://locations.dignityhealth.org/dignity-health-arizona-specialty-hospital-chandler-az', 'https://www.eq3.com/ca/fr?utm_source=Yelp&utm_medium=yelphttps://www.eq3.com/ca/en?utm_source=Yelp&utm_medium=yelphttps://www.eq3.com/ca/fr?utm_source=Yelp&utm_medium=yelp&src_id=CHL40SCL012-ACT0007-Undf-INT0000', 'http://www.honzolandscape.com', 'https://www.starbucks.ca', 'http://k9cleveland.com', None, 'https://www.branhamlaw.com', None, 'http://slymanstavern.com', 'http://gap.com/', 'http://www.snellingwebdev.com', 'http://www.thewatchrepaircompany.com/', 'http://www.desertpinesgolfclub.com', None, '1592424790', 'http://www.homegoods.com/tjx/store.aspx?id=496', 'http://www.barriquesmarket.com/', 'http://www.arrowheadlanes.com', 'http://www.phoenixneurologicalinstitute.com', 'http://www.signsandprintinglv.com', 'https://www.franks-pizzeria.com', None, None, 'http://communitybridgesaz.org/', 'http://www.pendletonpediatrics.com', 'http://www.steinmart.com', 'https://haircutmenpeoriaaz.com', 'http://www.ahome4spot.com', 'https://www.livingspaces.com/stores/gilbert', 'https://www.washingtonstdiner.com', None, 'http://www.southernstylevegas.com', 'http://www.lhmaz.com', 'http://www.amykoch.com/', 'http://www.metropizza.com', 'http://www.scarizona.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.bowlofheaven.com', 'http://99only.com/store/Phoenix---12th-St./', None, None, 'http://www.harbordhouse.ca', 'https://storelocations.ae.com/us/az/phoenix/4550-east-cactus-road.html', 'http://studiovervepilates.com', '1592424862', 'http://www.sushiqueengrill.weebly.com', 'http://www.vegasvoiceinstitute.com/', None, 'http://www.farathomas.com', 'https://orchardplumbing.vegas', 'https://insomniacookies.com/locations/store/1195', 'http://clearprotectionusa.com', 'http://www.vervebeauty.com', 'https://www.libertygmcaz.com', 'http://www.vexperformance.com', 'http://deciem.com', 'http://www.mikesgarageaz.com', None, 'http://www.scrapsoflove.com', 'https://www.wyndhamhotels.com/hotel/08593?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:08593', 'https://www.cubesmart.com/arizona-self-storage/glendale-self-storage/301.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'http://www.ranchlandsdental.com', 'https://www.frysfood.com', 'https://locations.nekterjuicebar.com/ll/US/NC/Charlotte/2725-South-Blvd?utm_source=yelp&utm_medium=link&utm_campaign=South-End&utm_content=URL', None, None, 'http://www.theherbanlegend.com', None, 'http://www.arizonafarmersmarkets.com/pageRoadrunner/roadrunner.htm', None, '1592424929', 'http://www.sheetz.com', 'http://www.thepuppysplace.com', '1592424936', None, 'http://www.safesplash.com/locations/north-las-vegas-nv', 'http://www.joescustomaudioaz.com', 'http://project-sushi.com', None, 'http://abcjetski.com', None, None, None, None, 'http://www.saucepizzaandwine.com/locations/mesa-dana-park-mall/?utm_source=yelp&utm_medium=social', 'http://www.mpsaz.org/rmhs', 'http://www.shaggyscarpetcleaning.com', 'http://charlotte-southpark.barmethod.com', 'https://www.t-mobile.com/store-locator/az/gilbert/e-warner-rd-s-val-vista-dr?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.browmepretty.com', None, 'http://www.montrosekia.com', 'http://www.houseofwisconsincheese.com', 'http://www.sanmonteroapartments.com', 'http://linktr.ee/LauraHarbisonRealEstate', 'http://www.shahealth.com', None, 'https://shop.nordstrom.com/st/nordstrom-ross-park#restaurants?cm_mmc=yelp-_-ycm-_-rest-_-32237', 'http://www.krispykreme.com', 'https://www.highandryeaz.com', 'http://www.romeospizza.com', None, 'http://www.clevelandairshow.com', '1592425008', 'http://onestopnutrition.com', None, 'https://info.seniorlifestyle.com/senior-living/?utm_campaign=327&state=Arizona&utm_medium=cpc&utm_source=yelp&city=Sun+City', 'https://www.goddardschool.com/phoenix/chandler-boulevard-az?utm_source=yelp&utm_medium=business_listings&utm_campaign=school&utm_content=main_button', None, 'https://www.crazypita.com', None, 'http://www.renaud-bray.com', 'http://www.remax.com/realestateagentoffice/lasvegas-nv-89128-sandrathomas-id11154472.html', None, 'https://locations.riteaid.com/locations/nj/beachwood/93-atlantic-boulevard.html', 'http://www.scottsdalecheckcashing.net', 'http://www.lafayettedentallab.com', 'http://angelmobilemechanic.com', 'http://www.big5sportinggoods.com', 'https://www.getmovingservice.com', 'http://www.troncellitolaw.com', 'http://www.dairyqueen.com/us-en/locator/Detail/?store-id=10387&localechange=1', None, None, 'https://bainbridgebody.com', '1592425063', 'http://www.hhgregg.com', 'http://www.americanlaser.com', 'http://www.azjuniper.com', 'https://vindaloo-express-indian-cuisine.business.site', None, None, 'http://cashmanprophotolab.com/', '1592425082', 'http://www.squashrevolution.com/toronto-canada.html', None, 'http://www.shoemedic.com', None, 'https://www.supersmilevegas.com', 'https://www.frysfood.com/stores/details/660/00056?cid=loc66000056_gmb', 'https://www.riverbend.vegas', None, 'https://www.medexpress.com/location/pa/pleasant-hills/plp/?utm_source=yelp&utm_medium=paidsocial&utm_campaign=Evergreen', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.state48brewery.com', 'https://cccfurnishings.com', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Calgary-AB-T2Z4M8/058072/', 'https://onechurch.to', 'http://www.drycleaningworldakron.com', 'https://ad.doubleclick.net/ddm/clk/434422009;236814625;a', 'http://allpromovingservice.com', 'http://www.fornesslaw.com', 'http://vegassuntanning.com/', 'https://www.dunnedwards.com/directory/store-list/phoenix-008', None, None, None, None, 'http://armstrongsemporium.com/', 'http://www.dogbarcharlotte.net', 'http://kabobnkurry.com/', 'http://bensonlincolnpittsburgh.com', 'http://bakerschoolofmusic.com/', 'http://ccrsllc.com', 'http://www.caesars.com/thelinq/restaurants/squeeze.html#.U7uM_I1dUyM', None, 'http://freebergteam.pillartopost.com', None, 'http://www.yourgrape.com', None, 'http://www.yogalamar.com', None, None, 'http://www.terribleherbst.com/', None, None, 'http://www.bathandbodyworks.com', 'http://montesverona.com/', 'http://www.ftjco.com', None, None, 'https://techvillappliancerepair.ca', None, 'http://www.chicagoeatery.ca', 'http://www.shoprobinsonmall.com/stores/charleys-philly-steaks/', 'http://www.cjstalleyspub.com', None, 'http://99only.com/store/Las-Vegas---Beltway/', 'http://www.KentCheeseMonger.com', 'https://www.mazajloungecalgary.com', 'http://www.partsauthority.com', None, None, 'http://www.mydivecenter.ca', 'http://www.hofbrauhauspittsburgh.com/', 'http://www.lakemetroparks.com/parks-trails/lakefront-lodge', 'http://pizzamilano.net/', 'http://www.atlascinemas.net', 'http://simplepurecbd.com', None, 'http://www.bk.com', 'http://sunyourbuns.com/', 'http://www.superpumper.com', None, 'http://www.elitecabaret.com', None, 'http://tacoheadllc.com', 'http://www.mrchickencle.com', 'http://www.cineplex.com', 'http://truhitfitness.com/central-scottsdale/', 'https://www.thelittleclinic.com/storeHours?store=85100108', 'http://www.sushipalace.ca/staff/ste-rose-laval', 'http://www.SweetPeppersBar.com', 'http://www.sears.com', 'http://www.westinvegas.com', None, 'http://www.finsandfriendsaz.com', 'http://www.cowtownskateboards.com', 'http://www.cityofmadison.com/metro/planyourtrip/parkandride.cfm', 'http://www.froots.com', None, None, 'http://www.arialasvegas.com', 'https://eastvalleynutrition.com', None, 'http://www.healthysmilesdentallv.com', None, 'http://www.thegildedgirl.com', None, '1592425324', None, 'http://www.dancecharisma.com/', 'http://www.warriordash.com/index.php', 'https://broadview-nail-spa-nail-salon.business.site', 'http://villagemontessori.com', 'http://Soulyinspiredaz.com', 'http://www.tjmaxx.com', None, None, None, 'http://uniquedetailinglv.com', 'http://www.fivestartavern.com', 'http://www.nineteen10kent.com', 'http://locations.in-n-out.com/80', 'http://www.hattiescharlotte.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=7276', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', None, 'http://www.aplusmovers.ca', 'http://www.sallybeauty.com', 'http://xaviergonzaleslaw.com/', None, None, None, 'http://www.leeseafoodboil.com', 'https://www.timewarnercable.com/en/residential.html?cid=soc:yelp:hplink', None, 'http://www.mobile-autodetailing.com', None, 'http://www.winners.ca', 'http://www.hrvatibar.com/', 'http://www.nysdental.ca', 'http://mcmahonsicecream.com', 'http://www.binasbrowboutique.com', None, 'https://www.walgreens.com/locator/walgreens-10710+w+mcdowell+rd-avondale-az-85392/id=7387', '1592425412', 'http://www.uptowncoffeepgh.com', 'http://oliversalehouse.ca', None, 'http://www.ClassicBrideandFormals.com', None, None, 'http://www.eyesonregentsquare.com', 'https://1966big.wixsite.com/korechicken', None, None, 'http://freshco.com/stores/major-mackenzie-leslie/', None, 'http://drdougguitar.com', 'http://www.azelitesurgeons.com/', 'http://www.thelashlounge.com/salons/blakeney/', None, 'http://www.bellagiospa.ca/', 'http://www.modern-furniturestore.com', 'http://www.guitarshackohio.com', 'https://www.moes.com/find-a-moes/nevada/las_vegas/1277?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://storelocator.pepboys.com/pepboys/stores/glendale/63rd_and_bell/00779', 'http://www.effinitysolutions.com', 'http://www.greatclips.com', '1592425476', 'http://fiveguys.com/', None, None, 'http://www.deltaco.com', '1592425489', None, 'http://www.480termite.com/', 'http://nvspine.com/', 'https://www.target.com/sl/fairview-park/2266', 'http://www.actionhobby.ca', '1592425504', 'http://www.menchies.com', None, 'http://www.bk.com', 'https://www.vocicenter.com', None, 'http://www.rainforestflowershop.com/', 'http://www.homehardware.ca', 'http://www.JimmyJohns.com', 'https://theeggworks.com', 'http://www.freshii.com', None, 'http://barre3.com/fort-mill', 'http://martysmarket.com/', None, None, None, 'https://www.autozone.com/locations/az/gilbert/734-w-warner-rd.html', None, 'https://www.vans.com', 'https://locations.crackerbarrel.com/il/urbana/129/', None, None, None, 'http://LeavittEvictions.com', 'http://www.eevmc.com', 'http://www.bestautoaz.com', 'http://www.sleepontario.com', None, 'http://www.ModernDayAgent.Net', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, None, None, 'http://www.citrusmedical.ca', 'http://www.thecorporatedeli.net', 'http://www.valleyhonda.net/', None, 'http://www.hammersgrillandbar.com', 'http://www.thenichemarket.com', 'http://www.lkncomedyzone.com', None, 'https://www.halibuthouse.ca/locations/halibuthouse85kingstonroadeast/', None, 'http://www.la-z-boy.com', None, None, 'http://www.restorecoldpressed.com/', 'http://www.tresriospgh.com', 'https://stores.musicarts.com/concord-mills?source=LGOA5LKA', 'https://abrazoorthopedics.com/our-providers/jeffrey-copoloff-dpm/', 'http://chamberframer.com/', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB094', 'http://www.oldtowncycles.com', None, 'http://capellisociety.com/', None, '1592425635', None, 'http://olssonoptical.ca', None, 'https://www.petsmart.ca/stores/ca/on/vaughan-store2024.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', None, None, 'https://locations.davidstea.com/on-scarborough-28', 'http://www.themindfulnessclinic.ca', 'http://www.justduckytours.com', None, 'https://rightspacestorage.com/self-storage-locations/nevada/las-vegas-nv-storage-units/3043-N-Pecos-Rd/', None, 'https://www.e-arc.com/location/las-vegas-east-patrick-lane/', 'http://budandvine.com/', 'http://www.salon22.biz', 'http://www.sobeys.com', 'http://www.suncoastcasino.com/things-to-do/bowling?disid=wmm_yelp_sc_corporate_suncoastbowling_organiclink', 'http://www.ohbombay.ca', None, None, 'http://charmeck.org/mecklenburg/county/ParkandRec/Parks/ParksByRegion/SouthRegion/Pages/Idlewild.aspx', None, 'http://thainoodle.ca', 'http://www.ntb.com/store/8885/allison-park-pa-15101-2321?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'http://www.planetfitness.com/gyms/charlotte-whitehall-nc-125?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.sanpauloapartments.com', 'https://www.hihealth.com/hi-health-supermart-rural-university-tempe/', 'http://www.marlieqs.com', None, 'http://www.marios-spa.com/', 'http://www.annaslinens.com/?utm_source=Yelp&utm_medium=Annas_Homepage&utm_campaign=Yelp', 'http://theupsstore.ca/148', 'http://www.yeoldeorchard.com/fr/locations/saint-sauveur', None, None, 'http://www.mbautoworks.com', 'http://www.charmeck.org/', '1592425718', 'http://www.purrfurredpet.com', 'http://www.flourshopfood.com', None, 'http://www.lacasaditalia.com', 'http://www.churesto.com', 'https://markhummel.fathomrealty.com/agents/265318/Mark+Hummel', 'http://www.doggydazeaz.com', 'http://www.ultimatehairforcestudio.biz', 'http://beyondbeautycleaning.com', None, None, None, 'http://weeklyads.aldi.us/aldi', None, 'https://haircutmenwaterworkspittsburghpa.com', 'https://www.altimadental.com/locations/cedarbrae/', 'http://www.stouttent.com', 'https://f45training.ca/MississaugaDowntown/trial', 'http://www.tappo.ca/', None, 'http://www.brianchisholm.bhhsaz.com', None, None, 'http://www.stevesrestaurant.ca', 'https://www.chilis.com', 'http://www.softmoc.com', 'http://www.cutlersappliancerepair.weebly.com', 'http://www.safemanagement.net', 'http://www.wilfridpastabar.com', 'http://www.dynamicdentistry.net', 'http://www.dynomitecleveland.com/', 'http://www.consignmentsoncentre.com/', 'http://www.snowpalacecalgary.com', 'https://agents.farmers.com/az/gilbert/kevin-shelton?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://NevadaMobileMix.net', None, 'http://www.drjodialbertod.com/', 'http://www.lakesidedentists.com', None, 'http://hitsandmisses416.blogspot.com', 'http://pizzahut.com', 'http://www.fatwillysaz.com/', 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://www.mcdl.info', None, 'http://www.Eautospa.ca', 'http://www.susanhughesdesign.com', 'http://Www.boardandbrush.com/surprise', 'http://dream-retreats.com', None, 'https://www.autozone.com/locations/az/goodyear/1750-n-dysart-rd.html', 'http://mckeown.marketing', 'http://www.marriott.com/hotels/travel/yyzmk-courtyard-toronto-markham', None, None, 'http://www.nmtstudio.com', None, 'https://www.fobtoronto.ca', None, 'https://www.medvetforpets.com/location/medvet-pittsburgh/', 'https://www.washmenow.ca/', 'https://www.safeway.ca/find-a-store/store/8835-safeway-whitehorn', 'https://store.vioc.com/oh/parma/7899-day-dr-44129-060029', 'http://www.soggydoggyshop.com', '1592425876', None, 'https://arielcordero.com', None, None, None, 'https://www.gtogata.com', 'http://www.starbucks.com/', 'http://www.homeinstallers.ca', 'https://www.petpeoplestores.com/riverbend.html', 'http://us.uso.org/LasVegas', 'https://cocofreshtea.ca', 'http://www.gfixes.com', 'http://www.eyemasters.com', None, None, 'http://www.swplumbingservices.com', 'http://fitness1gym.com', 'https://www.robertsonfamilydentistry.com', 'http://www.djbuckproductions.com', '1592425922', 'http://www.familyvideo.com', None, 'http://www.drfeuer.com', 'http://www.losfavs.com/', 'http://www.mallingereyecare.com', 'http://www.adogslifetorontoinc.com', '1592425937', None, '1592425943', 'http://www.charlottelatindance.com', 'https://www.caesars.com/paris-las-vegas/things-to-do/pool?utm_campaign=Yelp&utm_term=SoleilPool&utm_medium=local&utm_source=yelp&utm_content=pool', 'http://www.happyhomespainting.net', 'https://www.pizzahut.ca/store-details/store-R29601/pizza-hut-PONT-VIAU', 'http://moms-deli.com', None, 'https://stores.loft.com/us/az/scottsdale/15211-north-kierland-blvd.html', 'http://www.starbucks.com/store/9334/', 'http://www.banfield.com/veterinarians/az/gilbert/gil?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.rotorooter.com/cuyahogafallsoh', 'https://georgebrazilhvac.com', 'http://www.rileyswinesoftheworld.com', 'http://www.asianfusion168.com', 'http://www.brindaliers.com', None, 'https://www.acmestores.com', 'http://www.lopezmartialarts.com', None, None, 'http://www.restaurant28bbq.com', None, 'https://www.cavecreekdentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.sonicdrivein.com/', 'https://www.medexpress.com/location/pa/pleasant-hills/plp/?utm_source=yelp&utm_medium=paidsocial&utm_campaign=Evergreen', 'http://www.fleetfeetfortmill.com', None, '1592426010', 'http://www.sincerelyyogurt.com/locations/bridgeville', 'https://sosfirstaid.ca/course-locations/mississauga-first-aid-cpr-training/', 'https://feetishspa.com', None, None, None, 'http://www.antiquemalls.com/stores/14674.aspx', None, 'http://www.calgarylashes.ca/', 'https://www.thaiexpressfood.com/stores/60340?latitude=36.0633189&longitude=-115.05253019999998', 'https://locations.wendys.com/united-states/nv/henderson/4450-e.-sunset-rd', 'http://www.union.wisc.edu/capitalcafe.htm', 'http://arcelectricalllc.com', 'http://www.adt.com', None, 'https://www.throughtheleash.com', 'https://www.speedycash.com/find-a-store/nevada/las-vegas/flamingo-and-jones?utm_source=yelpstorelocator&utm_medium=Affiliate&utm_content=afflink', 'http://www.luckysupermarket.ca', 'http://www.entrustedpets.com', 'http://www.nwcchildren.com', 'http://www.thesideyardlv.com', None, 'http://www.talkingstickresort.com/coffee-garden.aspx', None, 'https://www.saldivarlaw.com', None, None, 'https://dmakproductions.com', 'http://phoenixtrailersales.net/', None, 'http://www.7-eleven.com/?yelp=29384', None, '1592426085', None, 'http://rinkydinkminigolf.com', 'http://www.cattivopgh.com', None, 'https://www.kurevapes.com', 'http://www.fivebelow.com', 'http://www.immaculatemwd.com', 'https://www.ottawa.edu/ouaz/home/', 'http://phopadthai.com', 'http://corsboutique.com', 'http://www.northvalleyent.net', 'https://www.teambrettaz.com/?cmpid=W3ZQ_BLM_0006', 'https://stores.bestbuy.com/oh/mentor/7830-plaza-blvd-168.html/?loc=ns100&ref=NS', '1592426116', 'http://scottsdalefamilydentistry.com', 'http://www.lapizzettaaz.com', 'http://www.mileautorepair.com/', 'http://www.clevelandfitnessclub.com', None, 'http://www.waterdamageaz.com', None, 'https://licehappens.com/locations/nevada/', 'http://www.terribleherbst.com/', 'http://www.michaelpoor.com', 'https://mydeluxecleaners.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592426150', 'http://normansorchard.com', None, 'http://www.dkeatery.com', None, 'http://akaisushiakai.blogspot.ca', None, 'http://www.begim.ca', None, 'http://www.vegas3deyebrows.com', 'http://clevelanddrycleaners.com', 'http://www.oliverspublichouse.com/', None, 'http://2101chandler.com', None, 'https://www.deervalleydentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.masterchocolat.com', 'http://www.scottsdalestudioofmusic.com', 'http://www.redsmoke.ca/', 'https://www.bathdepot.ca/', 'https://www.tourniagarafalls.com', None, 'http://www.indulgecatering.com', 'http://www.bparlorsalon.com', 'https://www.drivingbuythebest.com', 'http://www.fatbastardburrito.ca', None, 'http://www.ihg.com/holidayinnexpress/hotels/us/en/whitby/ywtca/hoteldetail', None, None, 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', '1592426218', None, 'http://hoohavspa.com', 'https://jasminenailsspa.business.site', None, 'http://deavercrafton.com/', None, 'http://www.hmedical.ca', 'http://www.oralsurgeonsofcharlotte.com', 'http://www.clip-ityclop.com', 'https://find.shell.com/us/fuel/10010465-7201-e-cave-creek-rd/en_US', 'http://www.maximumairbrushtan.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', 'https://emcnv.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://altiuspgh.com', 'http://www.cycrr.org', 'http://www.downeasthome.com', '1592426264', '1592426267', None, 'http://www.reefculture.com', 'http://www.themorgroup.com/', None, 'http://chandlerpd.com', None, None, '1592426284', 'http://massageandyoga.center', 'https://www.tophatphotobooth.com', 'http://bighornlaw.com', 'http://www.eriksbikeshop.com/eriks-bike-board-ski-shop-madison-westside-WI-53719.aspx', 'https://www.luxor.com/en/nightlife.html', 'https://www.starbucks.ca', None, None, 'http://www.downtoearthnaturalfoods.ca', 'https://www.walmart.com/store/2768/mesa-az/details', 'https://www.thejoint.com/arizona/phoenix/arcadia-48011', 'http://www.hairplusbeautysupplylv.com/', 'https://calgarylibrary.ca', 'http://spacolis.com/', 'http://www.cleanlivingpoolandspa.com', '1592426326', 'http://www.scdentalgroup.com', 'http://www.myrosatis.com/store-details/Mesa%20Greenfield', 'http://www.attorneyrodolfogonzalez.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/2050+Gallatin+Rd+N-Madison-TN-37115/storeid=16031?cid=ps_ylp_2020', 'http://www.toryburch.com/', 'https://www.cinemark.com/pennsylvania/cinemark-north-hills-and-xd?utm_campaign=int&utm_medium=organic&utm_source=yelp&utm_content=yelp_listing', None, 'http://www.aroundtheclockplumbingaz.com', 'http://www.serenevegas.com', None, None, None, 'https://www.honorhealth.com/locations/specialty-care/honorhealth-virginia-g-piper-cancer-care-network-surprise?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-virginia-g-piper-cancer-care-network-surprise', 'https://fitbodyaz.clickfunnels.com/sales-page-yelp', None, None, 'https://www.a-aaakey.com/locations/key-storage-arizona-253/?utm_source=yelp&utm_medium=paid', None, 'http://www.siegelsuites.com/rent-apartment-las-vegas/mlk-las-vegas-apartments.php', 'http://www.metropizza.com', 'https://www.cellularsales.com/stores/verizon-4144-nc-hwy-49-s-harrisburg-nc-28075/', 'http://www.apollorestaurants.com', 'http://www.wubcoffee.com', None, 'http://www.dancedocs.com', 'http://www.peoriapoolsupply.com', 'http://www.theyogasanctuary.net/', None, 'http://clevelandpropertymanagement.com', None, None, 'http://www.smoothieking.com', 'http://cloud9cleaning.weebly.com', 'http://vineysauto.com', 'http://www.cakesnflakes.com', None, 'http://www.nofrills.ca/en_CA/storedetail.336.html', None, None, 'http://www.picturepeople.com/default.aspx?PK=e3adeef4-54b4-43c6-990a-619531e6637b', '1592426422', '1592426425', 'http://www.ecodryrestoration.com', 'http://phomymy.com', 'http://www.tropicalislandcaribbeanrestaurant.com', 'http://www.queens.edu/', None, None, 'http://menards.com', '1592426450', 'http://www.swisschalet.com', None, 'https://smallbarftmill.com', 'http://www.sababapgh.com/', 'http://livingkitchen.com', 'http://3gphotobooths.com', 'http://www.superstore.ca', None, 'http://chanostireshop15.wix.com/tireshoprepairmesa', None, 'http://www.ljhaircuts.com', 'http://www.twowaylv.com', 'http://wendys.com/', 'http://www.bathandbodyworks.com', None, 'http://www.activegreenross.com/asp/detail_dealer.asp?vIndex=29', 'http://www.burnhampaint.com/', 'https://www.sanbrisasapts.com', 'http://www.cartersoshkosh.ca', None, 'http://www.latoltecamex.com', 'http://www.dunkindonuts.com', None, 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', 'http://prideautoglass.biz', 'http://www.ericjamesinsurance.com?cmpid=L8KQ_BLM_0006', 'http://rays-smoke-shop.business.site', 'http://www.Lowes.com?cm_mmc=search_Yelp-_-Display-_-Peoria-_-IL', None, None, 'https://www.marineratsouthshoreslv.com', 'http://www.goodwill.org', None, 'http://www.llbean.com', 'https://ppsd.com', 'http://thepiston.ca', 'http://www.7-eleven.com/?yelp=29663', 'http://www.welcomehomelasvegas.org', None, None, 'https://mountainsidefitness.com/locations/scottsdale-shea/', None, 'http://thebeeshop.net', 'http://pulpjuiceandsmoothie.com', None, '1592426555', None, None, 'http://www.autocitync.com', None, 'http://www.standupscottsdale.com', 'https://www.crunchdonutfactory.com', '1592426571', 'http://www.dollarama.com', 'http://www.lalunarossa.ca', 'http://feetparadisereflexology.com', 'http://www.dunkindonuts.com', 'http://www.pizzahut.ca/', 'http://www.kiltrentalusa.com', None, 'http://www.goalieshop.com', 'http://www.jpheatingandcooling.com', None, 'http://www.bigbiteburrito.ca/locations/burritos-in-scarborough/', None, None, None, 'https://lagrandeorangegrocery.com', 'http://www.gatewaydentalcare.net', 'http://www.brewsbest.com', None, 'http://sidestogobbq.com', 'http://www.felichia.com', 'http://westvalleydetailing.com', 'https://www.rubytuesday.com/', 'http://ad.doubleclick.net/ddm/clk/283420830;110240480;l', None, 'https://www.gothamcentral.ca', 'http://www.starbucks.com/store/17653/', 'http://oglawncare.com', 'http://www.fallasstores.com', 'http://greatclips.com/', 'http://www.torontossc.com', 'http://phoenix.gov/skyharborairport/maps_food_shops/term4-shops.html', None, 'https://www.wyndhamhotels.com/hotel/03330?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:03330', 'https://towerliquorphx.com', 'http://www.sellersandnewel.com', 'http://www.bentleygallery.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.arcticbites.com', 'https://onekickgym.com', 'http://www.javajoes.ca', 'http://Ziggyspubandrestaurant.com', None, 'https://locations.theupsstore.com/az/sun-city-west/13940-w-meeker-blvd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://angeliasonline.com', 'http://www.greatclips.com/salons/9116', 'https://www.londondrugs.com/london-drugs-store-030-calgary/heritage-plaza-030.html', 'http://www.shopsydneys.com', None, 'http://www.noahhelps.org/locations/copperwood/', 'http://www.bootleggersaz.com', 'http://www.slimsaz.com', 'http://www.borders.com', None, 'http://coolcuts4kids.com/salondetail/default.asp?salonid=66002', 'http://westdale-mall.com', 'http://www.eurway.com', 'http://www.sandbaraz.com', 'http://www.3for2pizzawings.com', 'http://www.epiphanydermatology.com', None, 'https://www.homehardware.ca', 'https://stores.partycity.com/ca/ab/calgary/party-store-ca2145.html', 'http://www.MatlisMedical.com', None, 'https://www.dirtdogla.com', 'http://www.warzonematrix.com', None, 'http://www.repairguysaz.com', 'http://www.torontomarketco.com/front-st-foods/', 'https://www.redroof.com/property/nv/las-vegas/RRI797', None, 'https://www.ulta.com/stores/mesa-az-225', 'http://www.parkschevrolethuntersville.com', None, 'http://www.capitalfordcharlotte.com', 'http://www.JimmyJohns.com', 'https://www.interdent.com/gentle-dental/locations/az/gilbert/3877-s-gilbert-rd-dentist-office?utm_source=organic&utm_medium=yext', None, 'http://www.the480bar.com', 'https://www.lowes.com/store/OH-Northfield/1139', 'http://www.azoralsurgeons.com', None, 'http://www.arcadia4127.com', None, '1592426782', 'https://www.ruffleshair.ca', 'https://www.culinarydropout.com', None, '1592426793', None, 'http://www.shumansautoclinic.com/', 'http://www.rpgaspiping.com', None, 'http://www.7-eleven.com/?yelp=22886', None, 'http://www.youfit.com/location/chandler-7337', 'http://www.diamondcakes.com/', 'https://sonorancleaning.com', None, 'http://www.fawakyburst.com', None, 'http://www.kidsandcompany.com', 'https://theloosemoose.ca', 'http://www.redsealnotary.com', 'http://www.burritoboyz.ca/', 'http://www.longsshoes.com', 'http://www.pastabilities.ca/', 'http://www.austrianclub.ca/', None, 'https://www.starbucks.ca', 'https://www.rusklockandkey.com', None, 'http://www.auctionnation.com', 'http://www.thegoldguy-sw.com', 'http://www.vaughanpl.info/libraries/view/11', 'http://bakecode.com', 'https://backyardbocceflats.com', 'https://locations.jackinthebox.com/us/nc/charlotte/7725-pineville-matthews-rd', "https://www.brueggers.com/?utm_source=yelp&utm_medium=homepage&utm_campaign=mentor&utm_term=Bruegger's%20Bagels%20Home%20Page", 'http://www.soundwerksonbell.com', 'http://www.ddsdiscounts.com', None, 'http://danklebrunsonleedds.com', 'https://southwestrestorationdesign.com', 'http://po-ke.ca', 'http://purewaxbar.com', None, 'http://www.entebella.com', None, 'http://www.myroscoes.com', 'http://www.petvalu.com', 'https://worldsewcentre.ca', 'http://www.tuesdaymorning.com', 'https://store.vioc.com/wi/madison/3594-e-washington-ave-53704-GR0030', 'http://99only.com/store/Chandler/', 'https://palacestation.sclv.com/Dining/The-Charcoal-Room.aspx?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', None, 'http://www.brothersmain.com', None, None, None, 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.goldenfeetreflexology.com', 'http://www.subway.ca', None, None, None, 'http://blowngohairbar.com', 'http://www.redsbarbeque.com/', None, 'http://www.lasvegasirrigationrepair.com', 'http://www.bk.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'https://www.vaqueroscarneasada.com', 'https://athleta.gap.com/stores/nc/charlotte/athleta-7068.html', 'http://www.progressiveeyecarelv.com', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'http://repairmycomputeraz.com/', None, 'http://www.starbucks.com/store/15887/', 'https://thesaguaro.com/scottsdale/#eat-drink', 'http://www.nevadaoutdoorliving.com', 'http://www.dollartree.com', None, 'http://www.chadwickevents.com', 'https://www.solasalonstudios.com/locations/champaign-commons', 'https://fluno.com/smittys-study-pub.php', None, 'http://www.lindsay-palmsapts.com/?campaign_code=yelp_Lindsay_Palms_AZ_85204', 'http://www.stoneworksltd.com', 'http://www.Americantv.com', None, 'http://www.mark-taylor.com/arizona/pietra/?utm_source=yelp&utm_medium=listing&utm_content=visit-website&utm_campaign=Pietra%20Yelp%20Listing', None, '1592426997', 'https://hellmannstreeservice.com', 'https://www.kidsquest.com/location/greenvalleyranch/', 'http://palmgrovemhc.com/contact/', 'https://www.dairyqueen.com/us-en/locator/Detail/?store-id=5176&localechange=1', None, 'http://thelandnutrition.business.site', None, 'http://www.tuxedoroyale.com', 'http://www.thebutterwoodbakeconsortium.com', 'https://www.choicehotels.com/arizona/phoenix/comfort-inn-hotels/az350/rates', '1592427026', None, 'http://www.scottsdaleaz.gov/parks/horizon.asp', 'http://www.azpoolguru.com', None, 'https://azwings.business.site', '1592427041', 'http://www.scottsdalefa.com/', None, 'https://www.wyndhamhotels.com/hotel/52780?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52780', 'http://www.belindaspickles.com/', 'http://lvhome.com/', None, 'http://www.consigningwomenarizona.com', 'http://www.tlccarecenter.com', 'https://windowdepotcleveland.com', None, 'http://www.spanishhillswellness.com', 'http://www.vcahospitals.com/decatur/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Decatur_Animal_Hospital&utm_campaign=main_url', '1592427074', None, 'http://www.taxque.com', 'http://www.meckeye.com', 'https://hibachijapansteakhouse.com', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', None, '1592427093', 'http://www.searsauto.com/stores/6320', 'https://www.chilis.com', '1592427101', 'http://www.juiceandjava.ca', None, 'http://www.wildwingrestaurants.com', 'https://www.jacksonhewitt.com/Tax-Preparation-Services-Locations/SC/Rock-Hill/10605/', None, 'http://www.candcroofs.com', 'http://www.ironmanarizona.com', 'http://www.dignitymemorial.com/funeral-homes/lasvegas-nv/palm-south-jones-mortuary', 'http://divinelaser.wix.com/divinelaserandspa', 'http://www.bonannosnewyorkpizzeria.com/menu/flamingo-food-court/', '1592427129', 'http://www.theelfsquad.com', 'http://www.bestfriendspetcare.com/charlotte-nc/?utm_source=yelp&utm_medium=directory&utm_content=ad&utm_campaign=26_pvl', 'http://www.crossfitdoubledown.com', 'http://www.owllasvegas.com', 'https://www.caesars.com/cromwell?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=TheCromwellLasVegas&utm_content=hotel', None, 'http://www.ripetomatopizza.com', 'http://www.frogurt101.com', 'https://treetoptrekking.com/parks/stouffville/', 'http://www.villaserenaapartmenthomes.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXRB', 'http://www.spamadison.com/', 'https://www.carenow.com/locations/las-vegas/silverado-maryland', 'http://www.frysfood.com/', 'https://mymodernlaw.com', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', None, 'https://www.amazinglashstudio.com/studios/az/tempe/tempe-marketplace', 'http://www.indiagrillaz.com', 'http://organizedbygreyson.com', 'http://www.azreapm.com', 'https://anantahealth.ca', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://order.subway.com/Default.aspx', 'http://www.provincesdental.com/', 'http://lasvegasarc.salvationarmy.org', 'https://www.kidsquest.com/location/texasstationcq/', None, '1592427216', None, None, 'http://www.parexcellencegroundskeeping.webs.com', 'https://cascatagolf.com', 'http://www.phoenixpawnaz.com', 'http://www.tbcconsignment.com', 'https://www.firehousesubs.com/locations/sc/celanese-rd', 'http://www.ellasuncle.com', 'http://comfortnails.ca', 'http://www.dirtystopless.com', None, None, 'http://www.pizzahut.ca/', 'http://www.passport-photos-toronto.ca', 'http://www.highbranchbrewing.com', None, 'http://www.chickin.ca', 'http://www.heroburgers.com', 'http://www.valkenaargroup.com', 'http://www.estrellafallsdentistry.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.saveonfoods.com/store/seton', 'http://www.jiffylube.com', 'http://www.caporestaurant.ca', 'http://www.peasantcheese.com', 'http://www.mfcu.net', 'http://www.leadersforlifema.com', None, None, None, 'http://shop-task.com/pages/toronto', 'http://www.hollyankphotography.net', 'http://splendido.ca', None, 'http://www.streetsofnewyork.com', 'http://www.sunterramarket.com/st_DocLib/00C/villagemarche.htm', None, 'http://www.chapelhillsjewelry.com', None, 'http://www.gamestop.com/store/us/az/tempe/3674/tempe-marketplace-gamestop', 'http://www.victoriassecret.com', 'https://www.peonygardenbuffetco.com', 'http://travishitesdc.com', 'http://Totalautopros.com', None, 'http://www.bodyandsoultherapy.ca', None, 'http://www.modernathleticscience.com', 'http://evderm.com', None, 'http://www.hamptonbanquethall.com', 'http://www.philsebastian.com', 'http://www.mipueblometro.com', 'http://www.itsallaboutyouconcord.net', 'http://www.momijis.com/', None, 'http://www.SanTanAikido.com', 'http://www.phoenixplumbinganddrain.com', None, 'http://swensonsdriveins.com/food-truck/', 'http://www.darrenwellenreiterdentistry.com', 'http://www.dontbebroke.com/?utm_source=Yelp&utm_medium=Location%2BPage&utm_campaign=Yelp', None, 'http://www.nailsnv.com', 'http://www.pinpointpainting.com', 'http://www.tempelaundry.com', 'http://order.baskinrobbins.com/menu/baskin-robbins-361437', 'http://www.amorino.com', '1592427390', '1592427393', 'http://cineplex.com/Showtimes/any-movie/cineplex-cinemas-empress-walk', 'http://www.brighton.com', None, None, 'https://horizoneye.com', '1592427407', None, 'http://www.countertoprock.com', 'https://www.azbpi.com', 'http://www.starbucks.com/store/9229/', None, None, 'http://www.beehivebuzz.com/', 'https://autowhiplashrehab.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.michaellbleekerdmd.com', 'http://www.thebelvedere.ca', 'http://interior-logic.com/', None, None, None, None, 'http://www.mattachioni.com', None, 'http://mosheta.com', 'http://www.forcedairtech.com', None, None, 'http://www.enterprise.com/car_rental/deeplinkmap.do?gpbr=3946&bid=004&cnty=US&arc=YAPL100&cm_mmc=Yelp-_-Local-_-National-_-null', 'https://www.trappedescaperoominland.com', 'http://www.icedforlife.com/', 'http://www.goodlifefitness.com/locations/ontario/vaughan/milani-blvd?source=yelp-websitelink-vaughanmilani-gl', 'http://www.raidingtherockvault.com', None, 'http://www.aerotechdesigns.com/', None, 'http://www.drneilperko.com', None, None, 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=441', None, 'http://www.flipsideburger.com', None, None, 'http://www.dtbeautyfx.com', 'http://www.kakitchen.com', 'http://www.kelimccoy.com', 'https://stores.solsticesunglasses.com/solstice-sunglasses-fbc98c6077eb', None, None, None, 'http://SaylorRealEstate.com', 'http://www.prettyinpittsburgh.com', 'http://newdaycafelv.com', 'http://taylord.longrealty.com', 'http://Www.jackierenee.com', 'https://www.rickwestinsurance.com?cmpid=a9qq_blm_0006', 'https://www.jimmyjoesplumbing.com', None, 'http://Wrightawaymovers.wixsite.com/website', 'http://www.scallywags.ca', 'https://www.9round.com/fitness/mint-hill-nc-x4569', None, 'http://www.goldview.ca', 'http://www.rituselects.com', None, 'https://www.discounttire.com/store/az/phoenix/s/1018?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.pennsburypub.com', 'http://www.londongold.com', 'http://thegardenerskitchen.com/', None, 'http://countryanimalhaven.org', 'https://www.yogurt-land.com/locations/view/1310/mesa-dana-park?distance=2.7', 'http://www.bondshouseofcutlery.com', None, 'http://www.shoprevolution.com/', None, 'https://www.foxandhound.com/locations/huntersville', None, 'http://www.superiorschoolnc.com', 'https://www.ccfwobgyn.com', 'https://imescovered.com', 'http://www.abprospecting.com', 'http://www.pilateswithrenee.com', None, 'http://www.northshorepies.com', 'http://torontodistillery.ca/', 'http://www.roaddogtours.com/phoenix-brewery-tour', 'https://www.circlek.com/store-locator/us/glendale/9002-n-47th-ave/2702875', 'http://www.sunnyarizonapoolservice.com', None, 'http://www.yorkroadauto.com', 'http://www.robinsonpropertymanagement.net', 'http://yankeeclassicflooring.com', 'http://lasgorditasrestaurant.com', 'http://blacksheephair.ca', 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', 'http://www.dignitymemorial.com/funeral-homes/glendale-az/chapel-of-the-chimes-mortuary/2328', 'http://www.wigwamcreekdental.com', 'http://www.affordablecollisionlv.com', None, None, 'http://www.appletreetoronto.com', 'https://madisonsnyc.com/fr/', 'http://www.annaslinens.com', 'http://lasvegasclassiccoach.com', 'http://www.hawthornevalleygc.com', 'http://www.seedentist.com', 'http://www.ruthschrislasvegas.com', 'http://www.cakebakeshoppe.ca', 'http://joeys.ca', 'https://www.ghirardelli.com/locations-events/ghirardelli-locations/las-vegas', None, 'http://www.kathebarge.howardhanna.com', 'http://falbobrospizza.com', None, None, None, 'http://hairxpressionssalon.net', 'http://www.bankofamerica.com', 'http://www.justabitecheesecakes.com', 'http://www.danielsinthefalls.com', None, 'http://www.dolphinairaz.com', 'http://www.studioelie.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://malleys.com/stores/north-olmsted', 'http://hdbrowskinrx.com', '1592427738', 'http://www.narscosmetics.com', 'http://www.ampm.com', '1592427746', None, 'http://johnnyrockets.com', None, 'https://www.statefarm.com/agent/US/AZ/Mesa/Marge-Black-Graziano-WRP4V1YS000?cmpid=BZVG_BLM_0006', 'https://www.wyndhamhotels.com/hotel/17887?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:17887', 'https://locations.theupsstore.com/oh/stow/3732-fishcreek-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.lcbo.com', 'http://www.happyhalsmobilerv.com', '1592427769', 'http://www.lapoflove.com/Locations-North-Carolina-Charlotte', None, 'http://www.archiesdeli.com', 'http://www.thehummingbird.ca', None, 'http://www.carylackeylaw.com', 'http://www.azrapidprocess.com', 'https://www.pigglys.com', None, 'http://www.budgetlasvegas.com/locations', 'http://www.dchandymanaz.com', 'http://www.tailblazerspets.com/tailblazers-locations-calgary-inglewood.php', 'http://www.fitnleanxercise.com', 'https://locations.eileenfisher.com/us/az/scottsdale/womens-clothing-eus029.html', 'http://www.planetfitness.com/gyms/mentor-oh-1250?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.suarezpt.com', 'http://www.dwbistro.com/', None, 'https://www1.shoppersdrugmart.ca', '1592427817', 'https://www.firehousesubs.com/locations/al/madison', 'https://theflowershopaz.com', 'http://www.spraytanscottsdale.net', '1592427828', 'https://www.lifetime.life/life-time-locations/on-ajax.html?utm_medium=directory&utm_source=yelp&utm_content=homepage', 'https://secretgardenweddinglv.com', None, 'https://berrydivineacai.com', None, 'https://sweetfrog.com/locations/store/sweet-frog-fairlawn', None, None, None, 'http://www.arbys.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'https://www.jzbilliardsnv.com', None, 'http://Charlottecottageexpress.com', 'http://www.trs24-7.com', 'https://mountain-view-square.business.site', 'http://www.medicalexpress.ca', 'http://www.nvsphotography.com', 'http://www.roadrunnerlimousine.com/', None, None, 'http://restaurantkyoto.com', 'http://www.charleys.com/', 'http://www.surlatable.com', 'http://www.alegno.ca', 'http://www.musclemanmusic.com/', 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'http://vegasavguys.com/', 'http://www.mattressfirm.com', 'https://www.carstereostorepineville.com', 'http://thekabuto.com', None, None, 'http://www.nathansfamous.com/locator', 'https://www.novaksflowers.com', None, None, None, 'https://www.fcautodetail.com', 'http://www.thewickedwedge.com/', 'http://manchuwok.com', 'http://www.camelback.bhhsaz.com/', None, 'https://kabab-jwan.business.site', 'http://www.usstoragecenters.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/127+South+Main+Street-Davidson-NC-28036/storeid=6402?cid=ps_ylp_2020', 'http://www.jessicamitchell.com', 'http://www.beautifulimageantiaging.com', 'http://www.albertsons.com', 'http://www.threeriversinspection.com/', 'http://www.ncaqua.com', None, 'http://www.highrollerpizzeria.com', 'http://www.crossfithifi.com', None, None, 'http://makerpizza.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1212+South+Greenfield+Road-Mesa-AZ-85204/storeid=5026?cid=ps_ylp_2020', 'http://www.jacobsbarbers.ca', None, 'http://newmarkettoyota.ca/', None, 'https://www.dukesk9dashnsplash.com', 'http://www.lkwdpl.org', None, 'https://mrlockoutaz.com', 'http://www.goldenrulesalon.com', 'http://www.mickisalterations.com', 'http://mandiafandi.ca', '1592427998', None, 'http://www.aztreetrimmer.com', 'https://www.eyecareforyou.org', 'http://www.finegoldjewellers.ca/', 'https://www.canadaflowers.ca', 'http://www.dollarama.com', 'http://www.lushusa.com/', None, 'http://www.dsw.com', 'http://www.quiktrip.com', 'http://www.sweetgrassspa.ca', 'http://www.frysfood.com/', 'http://www.fionnmaccools.com', 'http://www.portofsubs.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, None, None, 'http://www.mdmphysicaltherapy.com', None, None, 'https://www.caesars.com/flamingo-las-vegas/shows/donny-and-marie?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=DonnyandMarie&utm_content=Entertainment', 'http://queenscityappliancerepairs.com', 'http://www.paletasbetty.com/', '1592428056', None, 'http://quickstartaz.com', 'https://www.target.com/sl/north-scottsdale/936', 'http://www.calgaryfarmersmarket.ca/vendors/view/bon-a-pet-treat', '1592428068', 'http://locations.jambajuice.com/ll/US/AZ/Scottsdale/15686-N_-Frank', 'http://www.chefofindia.ca/', 'https://www.gotastea.com', 'https://www.farmersmarkettempe.com', 'http://balancebeautyclinic.yolasite.com/', 'https://www.cccnevada.com/doctor/sapna-bhatia-md/', 'http://www.pizzapizza.com', None, 'http://www.treehousevegan.com/', None, 'https://www.kindercare.com/our-centers/pittsburgh/pa/073097?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=073097', '1592428097', 'http://www.midaslocator.com/AutoRepairFinder/tabid/151/Default.aspx', 'http://stores.newbalance.com', 'http://www.ckielphotography.com/', 'http://westolivefamilymed.com/meet-providers/nagma-s-lott-md/', None, None, '1592428112', 'http://www.m5modmed.com', None, '1592428120', 'http://www.johnstonmurphy.com', None, 'http://www.tidalwaveautospa.com/', 'https://locations.dignityhealth.org/dignity-health-medical-group-nevada-family-medicine-henderson-nv', None, '1592428135', 'https://www.valuecityfurniture.com/store-locator/pa/pittsburgh/451-clairton-blvd', 'http://www.demayolaw.com', None, 'https://www.blackmountainathenderson.com', None, 'http://www.oreillyauto.com', 'https://www.take5oilchange.com/locations/oh/solon-139/', None, 'http://www.smokerscorner.com', 'http://www.violinoutlet.com', None, 'https://stores.factory.jcrew.com/en/j-crew-mercantile-park-road-shopping-center', 'https://www.rsmsilks.org', 'http://www.comeandgetit.ca/', None, None, 'http://www.sunshineautorepairs.com/home.html', 'http://www.amazingcellulars.com', 'http://www.citrusguys.com', 'http://4teaandcookies.com', 'http://www.yogaroots.com', 'http://www.wholesalefashionshoes.net', 'https://www.libertypointeliving.com', 'https://www.unlimitedcollisionaz.com', 'http://www.thepeacefuldragon.com/', 'http://www.redtiecourier.com', None, None, 'http://ruchchiropractic.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://www.makkarbakers.com/', None, 'https://hot-dogs-el-caprichoso.business.site', 'https://draincleaning.vegas/index.html', 'http://www.royaltandoorigrill.com', 'http://www.azkidsdds.com', 'http://www.myphysio.com/clinic/detail/tobler-physical-therapy', 'http://www.unionhillsvape.com/', 'http://www.stellaandshay.com', None, 'http://spatacularskin.com/', 'http://www.mypermanentmakeupaz.com/', 'http://www.biketek.com', 'https://www.suncoastcasino.com/dine/fine-dining/salvatores', 'https://www.bellagio.com/en/restaurants/quick-eats.html', None, 'http://www.ichibanhibachisteakhouse.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/264+Trapelo+Road-Belmont-MA-02478/storeid=1848?cid=ps_ylp_2020', 'http://www.whichwich.com', None, 'http://shoerepair.oriti.com', None, None, 'http://www.crcwi.com', 'https://www.mayrik.ca', 'http://www.penskeautomotivecollision.com', None, 'http://www.evsm.net', 'http://www.urbanfarm.org', 'http://pinnaclefamilydoctor.com', 'https://www.zaxbys.com/locations/nc/charlotte/7508-s-tryon-st/', 'http://www.floordesigns-nv.com', 'http://www.club1pittsburgh.com', 'http://www.bilskidds.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://ad.doubleclick.net/ddm/clk/301028790;127996585;r?https://www.montecarlo.com/en/restaurants/diablos-cantina.html#/Latin%20Nights', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.walgreens.com/locator/walgreens-7628+penn+ave-pittsburgh-pa-15221/id=10345', 'http://www.lush.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.solarisdentistry.com', None, 'https://auto-spa.ca/mississauga-car-wash/', 'https://stores.advanceautoparts.com/oh/urbana/834-scioto-st-', 'http://glasscockdental.com', None, None, None, 'http://www.hoggys.com', 'http://www.tiltedkilt.com', None, 'http://www.sensicharlotte.com', 'http://kbautoglass.com/gilbert-autoglass-company/', None, 'http://www.villamadina.com/', 'http://www.brampton.ca/en/residents/Community-Centres/Cassie-Campbell/Pages/Welcome.aspx', 'http://www.mariecallenders.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592428365', 'http://www.elmwoodspa.com', 'https://vip3nailsandloungemcmurray.com', 'http://www.kfc.com/storelocator/Default.aspx?address=2023%20E%20Lake%20Mead%20Blvd,North%20Las%20Vegas,NV', 'http://www.ncdot.org', 'http://www.centralnightclub.ca', 'http://midnightsuntanning.ca/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.apnursery.com', 'http://www.cafeprovenceaz.com/', 'http://www.heynoodles.com', None, 'http://www.shawarmalicious.ca', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.acgatlantic.com', None, None, 'http://www.papworthhvac.com', None, 'http://www.faithlasvegas.org/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.crazymocha.com', 'https://www.havensalonhealing.com', 'http://www.dennys.com', 'http://brixwinesaz.com', 'https://www.mark-taylor.com/apartments/az/scottsdale/the-core/?utm_source=Yelp&utm_medium=reputation&utm_campaign=main', 'http://www.namvk.com/#new-page', 'https://www.sslexus.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', None, None, 'http://anchorpropertymanagement.com', 'https://www.azplumbers.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://crossfitweddington.com', 'https://www.lifetime.life/life-time-locations/oh-beachwood.html?utm_medium=directory&utm_source=yelp&utm_content=homepage', 'https://graebelmoving.com/cities/charlotte', None, 'http://www.rektdrones.com', 'http://ankajwl.com', None, None, None, 'http://www.starbucks.com/store/9298/', None, None, None, None, 'http://www.opulencecleaning.com', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2fpa%2fpittsburgh%2fwest-mifflin&sisearchengine=1524&siproduct=4518_Bus', 'https://www.mastercuts.com/locations/az/gilbert/mastercuts-san-tan-village-haircuts-2682.html', None, 'https://www.thebodyshop.com/en-us/?utm_source=yelp&utm_medium=yelp&utm_campaign=us_180418_w19_search_bau&utm_content=websiteurl', None, 'http://www.bowtiestuxedo.com/', None, 'http://www.bilibaloo.com/', 'http://www.sbarpgh.com/', 'https://www.francescas.com/store-locator/casa-paloma.do', 'https://www.orthocarolina.com/locations/detail/ballantyne', 'http://host.madison.com/wsj', 'http://martindaledental.com/appointments/toronto-king-st-west-dentist-office/', None, 'https://myhoneybakedstore.com/willoughby/8416', None, None, None, 'http://www.bottegaristorante.com', 'http://www.momstobeandmore.com/', 'http://www.fleetfeetmadison.com', 'http://bloombc.com/', None, 'http://lvobgyn.com/', None, 'http://www.fenixeatery.com', 'http://kaizenhealthgroup.com', None, None, None, None, None, 'http://www.tireconnections.com', 'http://thebanklasvegas.com/home', 'http://www.whatabagel.com', 'http://www.papajohns.com', 'http://www.arrowheadskincare.com', 'http://melonhead.ca', 'http://www.exclusivepaints.com', 'http://www.burgerinn.com', 'https://www.anytimefitness.com/gyms/2820/Elyria-OH-44035/?utm_source=yelp&utm_medium=local', 'https://www.thrivevet.com/locations/huntersville-north-carolina?utm_source=yelp-ads&utm_medium=cpc&utm_campaign=huntersville', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreID=954', 'https://www.kohls.com/stores/nc/matthews-249.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.fostersbakery.ca', 'http://mamas-indian-land.com/', None, None, None, 'https://stores.barnesandnoble.com/store/2254', 'https://www.redstarvapor.com/stores/vape-shop-scottsdale/', None, 'http://www.schillinghorticulture.com', None, 'http://bullheadcitypatiofurniture.com', 'http://arizonainterlock.com', 'http://www.signatureflight.com/', None, 'http://mylaundryroomphx.com', 'http://www.paheatingandac.com', None, None, 'http://www.thymetherestaurant.com/', '1592428637', None, None, 'http://www.lechateau.ca', 'http://GregLV.com', 'http://www.midas.com/lasvegas/store.aspx?shopnum=1192&dmanum=480', 'http://l.macys.com/akron-oh?cm_mmc=Yelp_Stores-_-Akron-_-n-_-577', None, 'http://www.rtcsouthernnevada.com/', 'http://www.brueggers.com/', None, None, 'https://www.kolbys.net', None, 'http://www.tich.ca/', 'http://www.costco.com/warehouse-locations/scottsdale-az-427.html', 'http://www.olivaeats.com', 'http://www.lasenza.com/ustorelocator/location/map', 'http://www.sandersonvolvo.com', 'https://www.midas.com/nashville/store.aspx?shopnum=3362&dmanum=608001', None, 'https://embassynailsbarcharlotte.com', None, 'http://www.fastmoversllc.com', None, '1592429013', 'http://northvalleyapplianceservice.com', None, 'https://www.vivint.com/ppc/protect?exid=207432&utm_source=yelp&utm_medium=display&utm_campaign=yelp_q3&utm_content=E__4x3iZxO78iJqs_cRz7w', None, 'http://www.restaurantmangiamo.com/trouver-un-resto/saint-eustache', 'http://massagemaniaglendale.com', 'http://www.kouskouscafe.com/', 'http://www.happyfootspa.ca/', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Las%20Vegas/NV/8114', 'http://www.onehealthurgentcare.com/', None, 'http://leftbanktoronto.ca', 'https://www.lasvegassocialsecuritydisability.com', 'http://www.plakagreekrestaurant.ca', None, 'https://www.midwaynissan.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://www.thelunchbagaz.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'http://southpointpethospital.com', 'http://earlscheibautopainting.com', None, 'http://www.merlenormanstudio.com/NC/PINEVILLE/mn-6944/', 'http://www.realtorkaywest.com/', 'https://www.smilesquadlv.com', 'http://www.statravel.com/', 'http://Grillgate.ca', 'https://www.purccoffee.com', None, 'http://breakoutcalgary.com', 'http://www.badabingpainesville.com', 'https://www.mccarthylawyer.com/our-locations/arizona/scottsdale/', 'https://www.walmart.com/store/2515/phoenix-az/whats-new', 'http://www.turfandsport.com', None, None, 'https://synshop.org', None, None, 'http://www.allprofenceaz.com', 'https://www.beautifulfloors.com/pages/penn-hills-carpet-store', None, 'http://www.petwellnessaz.com', None, None, 'http://muttmotelandmakeovers.com', 'http://doddcamera.com/', 'http://www.radisson.com/phoenix-hotel-az-85051/usapnix', 'http://www.quesada.ca', None, 'http://newleafdermatology.com', 'http://www.MatthewsMC.com', None, 'http://www.familydoctorsgv.com/', 'https://www.nofrills.ca/store-locator/Pancha%27s+nofrills+%28Eglinton+Ave.+W.%29/0104?storeId=0104', 'http://www.justicebrothersupick.com', 'https://www.weidner.com/phoenix/monterra-luxury-apartment-homes/switch_cls%5Bid%5D/47808/', 'http://www.wendys.com/', 'http://www.bostonmarket.com', None, 'http://www.mojobistro.com', 'https://www.walgreens.com/locator/walgreens-1654+n+pebble+creek+pkwy-goodyear-az-85395/id=12334', 'http://www.dunkindonuts.com', 'https://www.amalfispizzapasta.com', 'http://www.urbanbarn.com/store-locator/queen+west.do', 'http://www.piecloud.ca', 'http://www.pizzaville.ca', 'https://nevadaorthopedic.com', None, 'http://sharpedgebeer.com', 'http://sambalatte.com/locations/molasky/', 'https://www.sunpoolandpatioscottsdale.com', 'http://jodytheloanguy.com', '1592429201', 'http://www.bathandbodyworks.com', None, 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'http://www.thesalonspot.com', 'http://gorgeouslashlounge.com', '1592429220', None, 'http://superlubecarcare.com/westlakesl.html', None, '1592429229', 'www.roseandcrowncalgary.ca', None, 'http://www.tkscheesesteaks.com', 'https://firstclasshomeinspection.com', 'http://www.freshkitchen.ca', 'https://dnagencyinc.com', 'http://www.mentornissan.com', None, 'https://www.thetidesonbroadway.com/contact_us/', 'https://www.volvocarsofphoenix.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://comingnails.yolasite.com/', 'http://www.pizzapizza.com', 'http://www.stonecareofarizona.com/', 'https://www.bbvacompass.com/USA/AZ/Chandler/4060-W-Ray-RD/', None, None, None, 'http://www.shell.us', 'https://locations.tropicalsmoothiecafe.com/nv/henderson/10612-south-eastern-avenue', '1592434601', 'http://www.paradisebakery.com/store_indiv.php?stid=104', 'http://salsaritas.com', None, 'http://www.PapaPastry.com', 'http://www.villageicecream.ca', None, 'http://www.bentosushi.com', 'http://thehalalguys.com', 'http://www.drblasco.com', 'http://arizonasinus.com/', None, None, 'http://the-latestscoop.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044282947422&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'https://www.cottolawfirm.com', None, 'http://landiscyclery.com', 'http://funkysageyoga.ca', 'http://www.foddrillmotorsports.com', 'http://www.themintlook.com', 'http://www.kimberlyjarman.com', 'http://www.bajasoultaqueria.com/', 'http://www.9round.com/scottsdaleshea', 'https://maps4u.com', 'http://www.pampered-and-polished-nails.com/', 'http://www.fuzzystacoshop.com/', None, 'https://www.wynnlasvegas.com/dining/fine-dining/cipriani', 'https://www.ttc.ca/Subway/Stations/Main_Street/station.jsp', 'http://rosenmanpediatrics.com', 'http://www.harmonsolar.com', 'http://ravisoup.com/', 'http://www.familydollar.com', None, 'http://www.biseagal.com', None, 'https://www.gongchacanada.ca', 'http://www.vaughanmills.com', '1592434735', 'http://www.ayscomputerrepair.com', None, 'https://www.werecoverdata.com', 'https://www.rcwilley.com/location/Nevada/Las-Vegas-Nevada-Warehouse?utm_source=yelp&utm_medium=referral', 'http://www.tssdetailing.com', None, None, None, 'http://thedriproom.com', 'http://www.officemax.com', None, 'https://www.uniquenailbarsunbrite.com', 'https://www.thejoint.com/arizona/scottsdale/scottsdale-shea-48014', 'http://www.swallowsrealestate.com', 'http://www.blandfordhomes.com', 'http://www.lids.com', 'http://www.xpresscare.co/', 'http://apexpainspecialists.com/', 'https://gymvmt.com/clubs/edgemont/', 'http://www.gzcomics.com/locale.html', None, 'http://www.mgfreshconcepts.com', 'http://www.housespouse.com', 'http://www.juicycouture.com', 'http://www.sugarmountain.ca', 'http://www.countryviewvets.com/', 'http://www.henribendel.com/', 'http://blackearthlanes.com/', 'http://www.sevencrownstattoo.com/', 'http://www.ptnoodles.com', 'http://www.blowersgrafton.com', None, None, 'https://pumpitupparty.com/scottsdale-az', None, 'https://www.crestmontbuickgmc.com', 'https://www.signaturestyle.com/locations/on/woodbridge/first-choice-haircutters-51198.html', 'http://www.chezcora.com/en/breakfast-restaurants/ontario/Cora-Richmond-Hill-Vogell-Road', None, 'http://www.atomicrestaurant.com', 'http://www.fionnmaccools.com', None, 'http://www.masterpoolservicellc.com', 'http://www.starbucks.com', None, 'http://www.wadaatacos.com', 'https://www.ruralmutual.com', 'https://www.menswearhouse.com/store-locator/2512?utm_source=yelp&utm_medium=listing&utm_content=2512&utm_campaign=AZ', None, 'https://www.oxifresh.com/locations/az/mesa-carpet-cleaning?utm_source=yelp&utm_medium=social?promo_code=YP5000', None, '1592434928', 'http://www.theenglishgardenfloral.com/', None, 'https://www.circlek.com/store-locator/us/gilbert/888-s-higley-rd/2703373', 'http://www.yourcanyons.com', 'http://www.hairartstudios.com', None, 'http://www.boggsequipment.com', 'http://oldnavy.com', 'http://www.abcdcomputers.com', None, 'http://landing.trugreen.com/yelp?city=Mentor&state=OH&zip=44060&utm_campaign=ORGANIC&marketingpartner=9817', 'http://www.walkerrealtynow.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://arizonasunshineheatingandcooling.com', None, 'http://www.riverbleusteakandfish.com/', None, None, 'http://Outoftheblueaz.com', None, 'http://eosfitness.com', 'https://www.winners.ca', 'https://eatbbds.com', None, 'http://www.morethanpies.com', 'http://www.qwellnesscenters.com', '1592435024', None, 'http://www.villamassimorestaurant.ca', 'http://diaper-eez.com', 'http://oscarnailsandspatempe.com', 'http://tastemediterranean.wixsite.com/taste', 'http://www.bk.com', 'http://www.springvalegolfcourseandballroom.com', 'https://www.usps.com/', 'http://www.starbucks.com/store/14175/', 'http://www.goclarendon.com', 'http://www.ellemarcs.com', 'https://www.murphyorthodontics.com', None, None, 'http://www.swisschalet.com', '1592435067', 'http://www.thairapysalonlv.com', None, None, 'http://www.billstowing.biz', 'http://www.washmycar.com', 'http://www.blindstogo.com/en/stores/new-market?ua=Newmarket%2C+ON+L3Y+5H6%2C+Canada&rds=50', 'http://jump2itplumbing.com', 'http://www.promotorsportsaz.com/', None, 'http://www.sislerheating.com', None, 'http://www.dollartree.com', 'https://sophiespizza.ca/location/', None, 'http://www.summitmetroparks.org/ParksAndTrails/LibertyPark.aspx', 'https://www.haircutmensheascottsdaleaz.com', 'http://www.lsgaz.com', 'https://barrospizza.com', 'http://thelegacygc.com/custom.asp?id=944&page=53454', 'http://www.unionvillefestival.com/', None, 'http://5anddiner.com', 'http://appianway.com/', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, '1592435133', '1592435136', None, None, 'http://chandlerlibrary.org', 'http://www.macleodtrail.com/', 'http://www.nostranomadison.com/', 'http://Www.phochallenge.ca', 'http://www.parcmidtownapts.com', 'http://www.nandos.ca/restaurants/bay-street', 'http://www.idoweddings4u.com', 'http://www.1sourceinsurance.com', 'https://www.walmart.com/store/1598/phoenix-az/whats-new', 'http://www.agamecafe.ca', 'http://www.spadusoleil.com', 'https://www.signaturestyle.com/locations/il/urbana/borics-hair-care-urbana-crossing-haircuts-75459.html', 'http://www.guardianstorage.com/locations/all/fox-c', 'http://www.toolserviceinc.com', 'http://www.mississauga.ca/portal/residents/centrallibrary', 'http://www.thenush.com', 'http://www.afancypupharrisburgnc.com', 'http://www.sweetlulu.com/', None, None, 'https://locations.churchs.com/az-phoenix-7235', 'http://www.mattressfirm.com', 'http://www.acunaautomotive.com', 'https://terracecourtapartments.com', None, 'http://www.genefinkstire.com', 'http://stoughtoncinemacafe.com/', 'http://buzzelliair.com/about-us', None, 'http://www.radiantjewelers.co', 'http://www.westcoastkids.ca', None, 'http://www.azgnr.com', 'https://www.petsmart.com/stores/us/az/glendale-store0157.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.elencantorestaurants.com', 'https://www.circlek.com/store-locator/us/avondale/1595-n-dysart-rd/2706645', 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'https://www.drtangsdentallv.com', None, 'http://www.uniquevintagechic.com', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=clemf&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'http://www.poledancemoves.com/', 'http://www.mr-maid.com', 'https://www.barrettfinancial.com/jboillot/', 'http://www.frysfood.com/', 'http://www.paristattoos.com', 'http://www.timothys.ca', 'http://www.theshop.beer', 'http://www.ParkAndKingston.com', 'https://locations.wafflehouse.com/nc-charlotte-449', 'http://www.boomerslv.com/', 'http://curiosi-t.com/', None, None, None, '1592435275', None, 'http://www.lvlt.org', 'http://herbivore.to/', None, None, None, 'http://platosclosetscottsdale.com/', '1592435293', 'http://www.thaihouselv.com', 'http://www.rosemontresidences.ca', 'http://cannaclinictoronto.com', 'http://www.bobmassie.com/', 'https://turtlejacks.com/locations/oakville/', 'http://www.tacosrick-o.com', None, 'http://wrenchesnratchets.com', 'http://www.sutrafusion.ca/', 'http://www.thepreferredrealty.com', 'https://www.homedepot.com/l/Madison/TN/Madison/37115/720?cm_mmc=seo-yelp&', '1592435322', 'https://www.oilchangeservicetempe.com', 'http://physiotherapytoronto.com', None, None, 'http://www.tajessentials.com', 'http://www.bronzeontheglo.com', None, 'http://www.goodmortgage.com', 'http://ultimatecycles.net', None, None, 'http://www.champaign4rent.com', None, 'http://www.copps.com/', 'http://www.mgmgrand.com/restaurants/corner-cakes.aspx', 'https://www.pleshfamilychiropractic.com', 'http://www.greekislesrestaurant.com', 'http://www.starbucks.com/store/9298/', 'http://Onceuponachildglendale.com', 'http://www.hardees.com', '1592435373', None, 'http://www.somacafe.com', 'http://www.santasmotorcyclesupply.net/', None, None, None, None, 'https://www.homedepot.com/l/Fairlawn/OH/Fairlawn/44333/3841?cm_mmc=seo-yelp&', 'http://progress702.com', 'https://www.circlek.com/store-locator/us/akron/1281-copley-rd/m5612', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://vsonno.com', 'https://www.novanthealth.org/clinic-locations/novant-health-sports--performance-medicine---arboretum.aspx?fbclid=IwAR0U9au7_tOtupMfdIyh9Wo5rgFCsEVvFJH1aMR_yXoWosNkkA8EN1RZTLM', 'http://www.divebarcleveland.com', 'http://brandontigrett.com', None, 'http://www.onehourlasvegaselectrician.com/', 'http://www.JimmyJohns.com', None, 'http://greendogmobilegrooming.com', None, None, None, 'http://area51fireworks.com', 'http://www.mika-sushi.ca', 'http://www.gourmethouseofhongkong.com/', 'http://www.sweetaddictionlv.com', 'http://www.studiolagree.com', 'http://emergencychiropractic.com', 'http://laveencrossfit.com', 'http://anthonyizzi.com', 'http://www.houstonresto.com/restaurant/laval-centropolis/', None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', '1592437192', None, 'http://www.bigtimejerseys.com', None, None, 'http://www.metrolinaneurology.com', None, 'http://www.autismcenter.org/contact-us', 'https://www.thomasvilleaz.com', 'https://azcdps.com/locations/gilbert/', None, 'http://local.buckle.com/WI/MADISON/67/?utm_source=Buckle&utm_medium=Website&utm_campaign=Store+Locator', 'https://www.christopherssalonfairlawn.com', 'https://order.papamurphys.com/menu/papa-murphys-greenway', 'http://www.tonyks.com/', 'http://www.nervousdog.com', 'https://www.halibuthouse.ca/locations/halibuthouse3483kingstonroad/', None, 'http://restaurants.quiznos.ca/on/etobicoke/WESTMALL&CIVIC-M9C1E7', 'http://christinasauthenticmexicanfoodrestaurant.food-places.com', 'https://thegoodkarma.ca', None, 'https://www.mattressfirm.com/stores/az/phoenix/mattress-stores-phoenix-az-85032-7927.html', None, 'http://www.collegeloanfreedom.com', None, 'http://www.swingerscircle.com', 'http://www.phoenixfamilymedical.com/', 'https://www.alankoa.com', '1592437297', 'https://smalv.com', 'http://alwaysbff.com', 'http://www.bulkapothecary.com', 'http://www.Kureshiandcompany.com', None, None, None, '1592437322', 'http://www.abovethebarre.com', 'http://www.Jeffersontownlake.com', 'http://www.bellitaliapizzeria.com', None, None, 'http://www.dsechilicookoff.org/', 'http://www.dominos.com', 'https://www.frysfood.com/storeHours?store=66000623', 'http://www.bankofamerica.com', 'http://riffraffbarandgrill.com', None, '1592437360', 'http://hotboxstfood.com/', 'http://www.oliphantsgym.com', 'http://www.coopswings.ca', 'http://dhmgnv.org/', 'http://www.greatclips.com', 'http://www.longjohnsilvers.com/', '1592437383', 'https://www.smithsfoodanddrug.com/stores/details/706/00334', None, None, None, None, 'https://www.homedepot.com/l/N-Scottsdale/AZ/Scottsdale/85260/472?cm_mmc=seo-yelp&', None, 'https://locations.mrtire.com/ny/amherst/941-millersport-highway?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, None, 'http://motelbouldercitynv.com', None, 'http://www.actionglassaz.com', 'http://www.therealdarcyd.com', 'http://teainfusionaz.com', 'http://www.deesdancewear.com', '1592437441', '1592437446', 'http://arizonastudios.com/', 'http://www.carandale.com', 'http://www.topsliquors.com/tasteoftops/', 'http://www.harborlightsmusicwest.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'https://4u2-shawarma-and-steak.business.site', 'http://www.ithaca.ca', 'http://www.artisticsmarthomes.com/', 'http://www.killiandentalclinic.com', None, 'http://www.dunkindonuts.com', None, None, 'http://www.aamcotempe.com/', '1592437496', 'https://central-tea-house.business.site', 'http://www.cucinacucinamodernitalian.com', None, None, 'https://www.enterprise.com/en/car-rental/locations/us/oh/amherst-3930.html?mcid=iyp:8368400', 'http://www.ferrarasimportedfoods.com/', 'http://www.greengrotto.ca', 'http://www.balletetudes.net', 'http://www.californiaallstars.com/lasvegas', None, None, 'https://www.chapmandodge.com', None, 'http://www.a1mrlimo.com', 'http://www.goodwillsp.org/shop/retail-stores/pineville/', 'http://www.easylifeboba.com', None, None, 'http://regalnailslasvegas.com/', None, None, 'https://fastframe.com/lasvegas/about-us/?UTM_source=yelp/?UTM_medium=referral/?UTM_campaign=visitfastframetoday', None, None, 'https://www.cellphonerepair.com/madison-east-wi/', None, 'http://www.shanesribshack.com/university/', 'http://www.4starautosales.net', '1592437590', None, None, 'http://snipits.com/locations/hudson', 'http://sushigenji.com', None, 'http://livingtreeservice.com/', 'http://www.orbitmoving.com/', 'http://whiskeygrade.com', 'https://www.havenfurnitureaz.com', 'http://www.manhattanbagel.com', None, None, 'http://www.addisontaylorfinejewelry.com', None, None, 'http://ikea.ca/whitby', 'http://www.bantercleveland.com', 'http://www.leavergardner.com', 'https://stores.mattressfirm.com/az/chandler/mattress-stores-chandler-az-7932.html', '1592437664', 'https://prostylesbarbershop.com', 'http://www.lifewellnesshomehealth.com', 'http://www.thecleaningauthority.com/LasVegas', 'http://www.starbucks.com', 'https://www.petsmart.com/stores/us/nv/n-las-vegas-store1027.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://www.chandleraz.gov/residents/recycling-and-trash', 'https://www.starbucks.ca/store-locator/store/822/fairview-pointe-claire-6815-transcanadian-pointe-claire-qc-h-9-r-1-c-4-ca', '1592437695', None, None, None, 'http://urbanapizzam.wix.com/pizzam', 'http://www.healthfirsturgentcare.com', None, 'http://www.paninitrip.com/', None, 'https://www.get-go.com/', None, 'http://www.picadelis.com', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85255/787-near-pinnacle-peak/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-787&utm_content=website-link&howheard=IYE', 'http://www.yycfoodtrucks.com/trucksprofile/wilks', None, None, 'http://www.marriott.com/hotels/travel/pitok-courtyard-pittsburgh-shadyside', 'https://www.lowkeypianobar.com', 'https://toughmudder.com/mud-run-arizona?utm_source=yelp&utm_medium=cpc&utm_campaign=arizona_2018&utm_content=url', 'http://www.dunkindonuts.com', 'http://smogbusters.com', 'http://vnails-spatolleson.com', 'http://www.hendersonbrewing.com', 'http://www.vapor-rage.com', 'http://vistana411.com/', None, 'http://www.dollarama.com/fr/', 'http://www.ferrariofontario.com', 'https://clearwaterautospa.com', 'http://www.ilovebuoncibo.com', 'http://nanzhounoodlemesa.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXTE', 'https://www.saharadentalsummerlin.com', 'https://turtlejacks.com/locations/erin-mills/', 'http://www.dynamicimages.ca', None, 'http://belmontabbeycollege.edu/', 'http://www.greatharvestmentor.com/', 'http://www.wildwoodgrill.com', 'https://www.cashmoney.ca/find-a-store/alberta/calgary/bannister-and-macleod-trail', 'http://www.mooreairconditioning.com', 'http://piratapgh.com', 'http://www.Arizona.Cars', 'http://www.firestonecompleteautocare.com/store-detail/13307?lw_cmp=YLP_FCAC_85031&utm_medium=FCAC_85031&utm_source=YLP', 'http://stonewatersalonandspa.com/', 'http://www.mrhandyman.com/cleveland-northwest-suburbs', None, 'http://www.onohawaiianbbq.com', 'http://www.gaiacleaningspecialists.com', 'https://redoakcalgary.ca', None, 'http://www.einsteinbros.com/', '1592437872', None, None, None, 'https://instyleflooringanddesigns.com', 'http://www.maxinebloom.com/', 'http://www.bergemazda.com', None, None, 'http://industrypgh.com', 'http://rtbsimmons.ca', 'http://www.glendaleazlibrary.com', 'http://www.pittsburghautotransport.com', 'http://theopticalexpert.com', 'http://www.harveys.ca', 'http://stuntdogcomics.com', 'http://www.brophyprep.org/', None, None, 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB138', None, None, 'http://www.wildwingrestaurants.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700006432139162&ds_s_kwgid=58700000444980784&ds_url_v=2', None, 'http://www.southparkpediatricdentistry.com', 'http://www.littlecaesars.com', 'http://www.53xlv.com', 'http://www.scottsdaleweightloss.com/', 'http://WAGZpetresort.com', 'http://www.pizzanova.com', 'http://thepizzacompany.biz', 'http://arizonawine.org/event/the-grand-wine-festival', 'http://www.anyandallautopartsnv.com', 'http://www.bsuitemadison.com', 'http://www.The519.org', 'http://www.UndergroundFitnessAZ.com', 'http://www.homedepot.ca', 'http://www.samuraisams.net', 'https://www.psychemedics.com', 'http://www.foxspizza.com/locations/pa/turtle-creek/turtle-creek-pa-222/index.html', 'https://www.flooranddecor.com/store?StoreID=180', None, 'http://ritasburritos.com', None, 'https://www.speedway.com', 'http://azcarpetmedic.com', 'http://www.autodetail-bay.ca/', None, 'https://www.popeyes.com/store-locator/store/restaurant_84824', None, 'https://www.mainstreetcoffee.co', 'http://locations.lifelabs.com/details/ON/Toronto/107/', 'http://www.roseandsonsswan.com/', None, 'https://www.chick-fil-a.com/greatlakesmall', 'http://www.ferragamo.com', 'https://www.nationalcar.com/en/car-rental/locations/us/az/mesa-gateway-airport-50v5.html?mcid=iyp:8368400', None, 'http://www.magnotta.com/MGHome.aspx', None, 'http://pushmodelslv.com', 'https://asmcmd.com/team/peter-w-mitchell-md/', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://www.ivebeenbitten.com', 'http://www.skatetrue.com', None, None, 'https://order.subway.com/Default.aspx', None, 'https://www.georgeskitchenphx.com', 'https://www.americanstandardair.com/how-to-buy/find-your-dealer.html', '1592438109', 'https://www.chick-fil-a.com/santanvillagemarketplace', '1592438116', None, None, None, 'http://eliteautomotive.vegas', 'http://www.clearviewinspects.com', 'http://www.thecathouseinc.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.rpmexclusive.com/', None, None, 'http://www.muchoburrito.com', 'http://www.simplegourmetpa.com', None, 'http://www.dontortaco.com', 'http://www.soundwerksonbell.com', 'http://www.serviceking.com/locations/service-king-deer-valley?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://beaucoupsaloninc.com', 'http://www.cascadevalleydental.net', 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://mosaicsoutheastasian.business.site', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, 'http://www.countyofdane.com/lwrd/parks/token_creek.aspx', 'https://barre3.com/studio-locations/northpeoria', 'http://www.toyourdoormobilehairstylist.com', None, None, 'http://www.fantasticsams.com', 'http://www.pghcw.com', None, 'https://www.riverdalemac.com', 'https://www.topnotchtransportation.com', None, None, 'http://www.starbucks.com/store/10759/', 'http://pizzaromamoon.net', '1592442461', 'https://locations.wafflehouse.com/az-phoenix-1489', None, 'http://blurnightclubaz.com/', 'http://www.quiznos.com/restaurants/PA/Monroeville', 'http://www.allthingstea.ca', None, None, 'http://lendingtree.com', 'http://www.peaceloveandlittledonuts.com', 'http://fugodesserts.com', 'http://www.legendsranch.vegas/', None, 'http://camillescafecharlotte.com', '1592442508', 'https://www.aaausedcars.co', 'http://caspirestaurant.com', 'http://www.azprecisiongraphics.com', 'https://www.yourmomsdonutsnc.com', None, 'http://robertostacoshop.com', 'http://www.pitaland.ca', 'http://www.skylandfoodmart.com', None, 'http://www.delta.com/', None, '1592442543', 'https://cactilandscape.com', 'http://www.fuegorestaurantgroup.com', 'http://atozautocare.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CAKSI', 'http://elitetrimworks.com/', 'https://www.smartstyle.com/en-us/locations/nc/charlotte/located-inside-walmart-1464-haircuts-18774.html', 'http://www.phoenixmobilewelding.com', 'http://www.rightway.com/cleveland-oh-dealership', 'http://gioninosmentor.com/', '1592442575', 'http://masterkimslv.com', None, 'http://www.ubgre.com/agent/pj-selby/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLECI', 'http://www.starbucks.com', 'http://www.eyedoctorscleveland.com', 'http://www.groomingdaleslasvegas.com', None, 'http://www.racewaycarwash.com', None, 'http://www.auntieannes.com', 'http://www.porkyourhunger.com', 'http://arialasvegas.com', None, 'http://www.mrhero.com', 'http://www.gladstonehotel.com', 'http://www.ruVilla.com/', '1592442635', None, 'https://www.shoppinggreatnorthernmall.com/directory/le-grand-orchid-nail-salon-spa', 'https://fathersondrywall.com', 'https://www.statefarm.com/agent/us/az/phoenix/susan-cox-7mbn11ys000?cmpid=gya9_blm_0006', 'http://www.freshtouchmedspa.com', 'http://lvee.vegas', 'http://www.aznypdpizza.com', 'http://catchit.ca/', None, None, 'http://www.grindfitnessaz.com', None, 'http://yamatosushi.ca', None, 'https://shop.nordstrom.com/st/nordstrom-yorkdale-shopping-centre#restaurants?cm_mmc=yelp-_-ycm-_-rest-_-30834', 'http://www.billsmidwayautobody.webs.com', None, None, 'http://www.papoustapandgrill.com', None, None, 'http://www.cerezocalgary.com/', None, 'http://www.arizonagaragedoorandrepair.com', 'https://cyclebar.com/location/scottsdale-101', 'https://www.queenannerestaurantandbar.com', None, 'http://beair.com/', None, None, None, 'https://www.outrageousoliveoil.com', None, None, 'http://www.browzeyeware.com', 'http://www.Vtheater.com', 'http://www.willycreations.com', None, 'http://www.seafooddepot.ca', None, 'https://agent.amfam.com/southwest-valley-associates/nv/las-vegas/7345-s-durango-dr-ste-108/', 'http://www.lcbo.com', 'https://www.mcclintockhvac.com', 'http://www.skylinemovingandstorage.com', '1592442779', 'http://www.relaxtheback.com/stores/mesa', 'http://www.mobil.com', None, 'http://www.sugarfactory.com/', None, None, 'http://www.kfc.ca/store/sunrige-mall-101-2525-36-st-ne-calgary', 'http://www.bedwellvanlines.com', 'http://insightpestcleveland.com', None, 'https://sweetfrog.com/locations/store/huntersville-nc', 'https://may-yan-seafood-restaurant.business.site', 'https://www.marks.com/en/stores/calgary-macleod-6636-macleod-trail-sw-chinook-station.html', 'http://www.gisautomotive.com/', 'http://www.riverhardwoodfloorsinc.com', None, 'http://stores.lanebryant.com/wi/madison/plus-size-clothing-madison-wi-6481.html', None, 'http://aspotlesshouseaz.com', 'http://www.mimicocruisingclub.com', 'http://www.jabzboxing.com/arcadia', None, 'http://sanctuarybeachwood.com/', 'http://www.torontopubliclibrary.ca', 'http://www.caitlinaudreyphoto.com', None, 'http://cactusgaragedoors.net/', None, None, None, None, None, 'http://www.littlecaesars.com', '1592442871', None, 'http://www.Tillerman.com', None, '1592442880', 'http://www.portoladelsol.com?campaign_code=yelp_Portola_Del_Sol_NV_89106', 'http://www.internationalcentre.com/', None, 'http://www.a-32.com', 'http://www.sumosnow.com', 'https://www.rootsnaturalkitchen.com', 'https://locations.jackinthebox.com/us/az/mesa/525-n-stapley-dr', 'https://north.laboccapizzeria.com', 'http://www.lebalthazar.ca', 'http://www.mustangcarpetandtile.com', None, 'https://www.sportchek.ca/stores/maple-leaf-square.html', None, 'http://www.hirshdermatology.com', 'http://www.southparkoptical.com', 'http://www.maximusnutritionaz.com', 'http://www.freewayinsurance.com', 'http://thebroadviewhotel.ca', 'http://www.applebeescanada.com/default.aspx', 'http://www.executivelounges.com/lounges/calgary-rocky-mountain-airport-lounge', None, 'http://www.keenedgeaz.com', 'http://www.PhoenixHomesHQ.com', 'http://www.metroparks.cc/lakeview-park.php', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.eatfitgo.com', 'https://Veronicaandco.salonsuitesolutions.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.fitbodycalgary.com', 'http://www.leisureunlimitedinc.com', None, 'http://www.weinsteinimaging.com/page.php?pg=Shadyside+Office', None, 'https://www.sephora.com/happening/stores/beachwood', 'http://www.tropicalsmoothiecafe.com', None, 'http://www.chaninni.com/', 'http://us.havaianas.com', 'http://www.tuesdaymorning.com/stores/search.html?q=1700+Deming+Way', 'http://www.heroburgers.com', None, None, 'http://www.southsiderswaxhaw.com', None, 'http://www.draincleaningsolutionsdcs.com', None, None, None, 'http://blauco.com', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://mgmgrand.mgmresorts.com/en/amenities/grand-salon.html', None, None, 'http://mrsub.ca', 'http://www.mathnasium.com/queencreek', 'https://icater.ca', None, 'http://www.mrbsmoonwalk.com/', None, 'http://www.bulwarkpestcontrol.com/', None, 'http://www.tulahotyoga.com', 'http://www.ardevents.com', 'http://www.allianceprofessionalmoving.com/', None, 'http://www.northroyaltonanimalhospital.com', 'http://www.alteredtails.org', 'http://www.rockinthehouse.com', 'https://stores.bestbuy.com/nc/charlotte/14125-river-gate-pkwy-1107.html/?loc=ns100&ref=NS', 'http://www.subway.ca', 'http://chase.com', None, None, None, 'http://www.lockmonkeys.com/', 'http://www.art-square.ca/', 'http://www.brickhousepizza.ca', 'http://sakawacoffee.com', None, None, '1592443079', 'http://www.clerkofcourt.maricopa.gov', 'https://www.firehousesubs.com/locations/oh/lorain-rd-water-tower', 'http://www.sticksandshakes.com', 'http://www.beisushi.com/', 'http://www.fantasticsams.com', 'http://www.swisschalet.com', 'http://bfpnv.com/', 'http://www.greywolfaccounting.com', None, None, None, 'https://www.maaco.com/locations/nv/las-vegas-12597/?utm_medium=bry&utm_source=yellowpages&utm_campaign=m2597', None, None, 'http://www.starbucks.com/', 'http://www.newyorkfries.com', 'http://www.adamcrobertson.com?cmpid=D0Z0_BLM_0006', 'https://www.myeyedr.com/locations/ballantyne?utm_source=Yelp&utm_medium=Referral&utm_campaign=ballantyne', 'http://www.scottsdaleskinandlaser.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.toysrus.ca', 'http://www.kitchbar.com/', 'http://www.SistinePlasticSurgery.com', 'http://www.mingcuisine.com', None, '1592443142', None, 'http://www.klfohio.com', 'http://www.coffeecove1.com', None, 'https://www.cubesmart.com/arizona-self-storage/chandler-self-storage/2.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'http://www.grimesinteriors.com', None, 'http://haroldschicken33.com', None, 'http://www.mandalaybay.com/dining/mix/', None, None, None, None, 'http://www.gardinermuseum.on.ca/visit/jamie-kennedy-at-the-gardiner', 'http://southwestautobodylv.com', None, None, '1592443187', 'https://furley.ca', 'http://lordnelsonsbargrill.weebly.com', None, None, 'http://www.tytinfitness.com', 'http://kojooriphotography.com', 'http://www.parkroadbarbers.com/', None, 'http://www.mywaterfordapts.com/', '1592443212', 'http://kaliopihookah.com', None, 'http://www.immigrationlawnv.com', None, 'https://chopstickonbloor.ca', 'http://www.casinoarizona.com', 'https://www.hungryhowies.com/store/hungry-howies-00610?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=610&utm_content=Website_Link', 'http://laurelwoodbooks.com/', 'http://hoaihuongrestaurant.com', None, None, 'http://parkwaydental.ca/', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.cancunparma.com', 'https://locator.chase.com/az/laveen/7241-s-51st-ave?jp_cmp=rb/LocalListings/aff/branch/na', 'http://apitstopgarage.com', 'http://www.tacticalrestoration.com/', 'http://www.socialitebar.ca', 'http://www.missiontreatment.com', None, 'http://www.fountainhillsdoctors.com/', 'http://www.fattuesdaywestgate.com', 'http://www.acerentacar.com', 'http://www.justbreathewellnesscenter.com', 'http://www.hamptondogcentral.com', None, '1592443279', 'http://www.sushihirolv.com', 'http://www.palazzotownhomes.com', None, 'http://www.permanentbeautybylisa.com', None, 'http://www.markhamandhairdentistry.com', None, 'http://www.deltaco.com/', 'http://www.thedoorescaperoom.com', 'http://sportinglifebar.com/', 'http://livingdeadtattoo.net/', None, 'http://www.lawlessdenim.com/', 'http://www.buybuybaby.com', 'http://www.shaggy2chic.ca', 'http://www.shakersfuncentre.com', 'https://www.associateddentists.com', 'http://foodsforlifetoronto.ca', 'http://www.lcbo.com', 'http://www.mplcuts.com', 'http://agnistudio.com', None, 'http://www.burrierservice.com', 'http://allcityrefrigeration.com/', 'http://www.udderdelightsaz.com', 'http://www.infinitecables.com', 'http://www.thebagelstop.com', None, 'http://www.CallReneeEstateLiquidation.com', 'http://www.acgamesonline.com/', None, 'http://www.madefoods.com', 'https://www.mattressfirm.com/stores/az/fountainhills/mattress-stores-fountain-hills-az-85268-6655.html', 'http://www.maddoctordetailing.com/', 'https://www.olivegarden.com/locations/az/phoenix/metro-center/4410?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:phoenix-az-4410_pl:locurl_rd:1754', None, None, 'http://www.bbtoronto.com/aupetitparis', 'http://www.ae.com', 'http://www.scottsdaleaz.gov/Police', 'http://toysrus.ca', 'https://www.capadancer.com', 'https://jkaraoke.multiscreensite.com', None, 'http://www.calgarysurgery.ca', 'https://www.eyeglassworld.com/store-list/pittsburgh-pa-15237/', None, None, None, 'http://www.buttonboy.net', None, '1592443412', 'http://www.npiweb.com/grant', '1592443418', None, 'http://www.allproplumbingaz.com', 'http://www.fountleather.com', 'http://valleyhortservices.com/', None, 'http://www.icenownv.com/', 'https://lawnlove.com/las-vegas-lawn-care?utm_medium=ListingTraffic&utm_source=Yelp', 'http://www.toryburch.com', 'http://www.93harbord.com', None, 'https://www.garagedoorservice.com/phoenix', 'http://www.arrowheadflowers.com/?srccode=yelp_track', 'http://www.boxandbowshop.com', None, '1592443453', 'http://mylasvegasdesigner.com', None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=2179&localechange=1', 'https://www.questcarpetstonecarechandler.com', 'https://www.sephora.com/happening/stores/toronto-eaton-centre', None, 'http://www.code3er.com', 'http://www.filibertos.com', None, 'http://tinyteeth.com', 'http://diamondcraft.jewelershowcase.com', None, 'http://fvfoods.ca', None, 'http://powpizza.ca', 'https://www.bodicafe.com', '1592443502', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://cilantrocalgary.com', 'http://thedonutscene.food-places.com', None, 'http://www.thomaslogisticsllc.com/', 'https://www.camdenliving.com/charlotte-nc-apartments/camden-stonecrest?cm_mmc=Yelp-_-AROC-_-Charlotte-_-camdenstonecrest', 'http://www.claryspopcorn.com', '1592443528', 'http://www.rossstores.com', 'http://www.thespokeeasyclt.com', None, 'http://urbanexchangeclothing.com', 'http://www.vegashomefurniture.com', None, 'https://shakeysdeluxetattoo.com', None, None, 'https://www.wellsfargo.com', 'https://queenswaymattress.com', None, None, 'http://www.southcalgarymedicalclinic.ca', 'http://locations.smartandfinal.com/nv/las-vegas/728/', 'https://www.smoothieshopscottsdaleaz.com', 'http://www.archtopcafe.com/', 'http://www.gscsecurity.com', 'http://www.sunnybrook.ca/', 'http://www.bouldersonsouthern.com', 'http://www.kbproductioncanada.ca', None, 'http://melonhead.ca', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'http://www.bigotires.com/regions/Nevada', 'http://www.goldendaysco.com', 'http://1stchoiceplumbingaz.com', 'http://alleykattattooaz.com', 'http://www.buckle.com', 'http://www.mazdadelaval.com', 'http://www.bodyrevivalspa.com/', 'http://eSMIL.com', 'http://JonesMediaPublishing.com', 'http://www.villaitaliankitchen.com', 'http://stingraysushi.com/', 'https://www.walgreens.com/locator/walgreens-10+pitts+school+rd+nw-concord-nc-28027/id=10253', None, 'http://www.serenityhospicelv.com', 'https://locations.wendys.com/united-states/al/madison/8814-hwy-20-w', 'https://www.target.com/sl/strongsville/985', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592443665', 'http://www.montypythonsspamalot.com', '1592443673', None, '1592443680', 'https://www.smartstyle.com/en-us/locations/az/mesa/located-inside-walmart-2768-haircuts-18263.html', 'http://www.wokbox.ca/store28', None, 'http://www.hypnoticsalon.com', 'http://www.wynnlasvegas.com', None, None, 'http://www.castillons.com/', None, 'http://www.centuryhouseinc.com', 'https://www.justincrediblehairs.com', 'http://www.usanails.com', 'http://www.amr.net', 'http://southernsaladsandsandwichcompany.com', 'http://www.jpco.ca/', 'http://www.target.ca/en/', None, 'http://www.702sunrisedental.com', None, 'https://cobblestone.com/?utm_source=yelp%C3%8A', None, None, 'http://www.tvalskincare.com', 'http://www.pjsperformance.com', 'http://potagoldadventures.com/locations/phoenix-arizona-white-tank-stables/', 'http://www.crepedelicious.com', 'http://www.koshergourmet.ca', None, 'http://www.702sunrisedental.com', None, None, None, None, None, 'https://www.midas.com/phoenix/store.aspx?shopnum=1239&dmanum=684001', 'http://www.novammj.com', 'https://www.royalcleanerslv.com', 'http://www.dollarama.com', 'http://www.beyondtheleash.ca', 'https://www.wellsfargo.com', None, 'http://www.7-eleven.com/?yelp=29384', None, None, 'http://tirepirates.ca', 'http://corsameccanica.com', 'http://www.snapfitness.com/mesa', None, 'http://www.staterideshop.com', 'http://www.afcmed.com/locations/tempe', 'http://polishednailsspalv.com', 'http://kakamarkham.com', None, None, 'https://www.olympusproperty.com/olympus-steelyard-chandler-az/', None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.seafoodcity.com', 'http://www.brprop.com/', 'http://www.bluedevilgolf.com/', 'http://vintnerscirclescottsdale.com', 'http://www.pandaauto.co', 'https://desertbusterpestservice.com', 'http://www.tricitycardiology.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, None, None, 'http://www.illestnailvegas.weebly.com', 'http://thekettleblackpub.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___north_las_vegas', None, 'http://www.piesquared.com', 'http://www.BuySellManageHomes.com', 'https://tint-pro.business.site', 'http://www.kebabtime.ca', 'http://adadaink.com', None, 'https://azpreferredplumbing.com', None, None, 'http://crossroadsurbana.com', 'http://www.britishimportsnewmarket.com', None, 'http://www.couturebridals.com', 'http://mtbikeaz.com/trail-index/phoenix/hawes-trail-loops', None, None, None, 'http://www.bmoharris.com', 'http://www.sunglasshut.com/us/?cvosrc=display.yelp.LasVegas', 'http://www.theex.com', 'http://thetrophystop.net', '1592443952', 'http://www.FossilSalon.com', 'http://www.whitecastle.com', None, 'http://www.gourmetdelichandler.com', 'http://FCCMi.net', 'http://www.littleislandcomics.com', None, 'http://alternatordepot.com', None, None, 'https://locations.sonicdrivein.com/de/bridgeville/18757-u.s.-highway-13.html', 'https://lamadeleine.com?utm_source=yelp&utm_medium=organic&utm_campaign=2019-holiday', 'http://www.fruitonline.com', 'http://poppamaize.com/', 'http://www.snrgsalon.com', 'http://www.vinnysbcpizzeria.com', 'http://www.redroosters.ca', 'https://www.ferguson.com/branch/henderson-nv-plumbing', 'http://www.queenwestvets.com', None, None, '1592444003', 'http://www.ralphssnackbar.com', 'http://www.estaterealty.ca', 'http://www.eyecareopticalinc.ca', 'http://barretttaxlaw.com', 'http://www.ajimenu.ca', None, None, 'http://www.bordersstores.com', 'https://www.rubios.com', None, 'http://ipoolsaz.com', None, None, None, 'http://www.desertmobilervrepair.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'https://locator.chase.com/az/surprise/19500-n-sunrise-blvd?jp_cmp=rb/LocalListings/aff/branch/na', None, 'http://www.meowfoundation.com', 'https://www.tractorsupply.com/tsc/store_TOLLESON-AZ-85353_1906', 'http://www.theparadorinn.com', 'http://www.ultratans.com', None, '1592444059', None, 'http://www.sojournercenter.org', 'http://wizardofpaws1.com/', 'http://yogonovus.com/', 'https://www.menswearhouse.com/store-locator/4408?utm_source=yelp&utm_medium=listing&utm_content=4408&utm_campaign=OH', 'http://www.passagetoindiaaz.com', 'http://someburros.com/', 'https://www.plantarestaurants.com/location/planta-burger/', 'https://www.lacandco.ca', 'http://www.tollbrothers.com', 'http://www.meetingsandeventslasvegas.com/company/970255/', 'https://www.long-mcquade.com/location/Ontario/Toronto', None, 'http://www3.hilton.com/en/hotels/ohio/hilton-cleveland-downtown-CLEDOHH/dining/index.html', 'http://www.canon-blanc.com', 'http://rayscuisine.com', None, None, 'http://usdoodles.com', None, 'http://pulpjuiceandsmoothie.com', None, 'http://www.attncenter.com', None, 'http://www.wienerschnitzel.com', 'http://estebanmusic.com/', 'http://www.thetiresource.ca/', None, 'http://watsoninstallations.com', 'https://pizzanova.com/pizza-nova-vaughan-9960-dufferin-st/', 'http://theherbbox.com', None, 'http://www.randor.com', 'http://www.kilwins.com', None, 'http://www.magicoven.com', 'http://www.mamaisongourmet.ca', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', 'http://www.thecombineeatery.com/', 'http://www.lafontetrattoria.com', None, None, 'http://www.itechcustoms.com', 'http://www.hornaceksgolf.com', None, None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, 'http://www.newmarketautopro.ca', 'https://www.aritzia.com/en/store?StoreID=aritzia-southcentre-mall-calgary', 'https://www.wildwingrestaurants.com/location/king-city/', None, 'http://www.darice.com', None, None, 'http://www.ravefabricare.com', 'http://www.trendzrb.com', 'https://www.hilton.com/en/hotels/stoohhx-hampton-stow/?SEO_id=YELP-HP-STOOHHX', None, 'http://wbrvcomplete.com', None, 'http://www.expertautoequipment.com', 'http://bk.com/', None, 'http://www.azwomenshealthcare.com', 'https://www.frysfood.com/stores/details/660/00674', None, None, None, 'http://www.jeminihairartistry.com', 'http://www.chhistory.org/Places.php', None, 'http://www.ericksendental.com', 'http://www.brooklynpizzaparlors.com', 'http://www.greatskateglendale.com', 'http://cdclv.com', None, 'http://www.lapurabellaskincare.com/', 'http://www.mrcsrestaurant.com', 'http://ciaobabycatering.com', 'https://petmedic.vet/hospitals/northwest-animal-hospital/', None, 'http://www.mycomputercareer.edu/campus-locations/charlotte-nc', 'http://www.padremurphy.com/', 'http://www.dunkindonuts.com', 'http://www.badboy.ca/en/pg-storelocator-Brampton', 'http://lastilistasalonandspa.com/', None, 'https://www.22slate.com', 'http://www.alibabas.ca', 'https://www.squaretrade.com/go/locations/charlotte?utm_campaign=charlotte&utm_source=yelp.com', 'https://www.littledealer.com/pages/location%20phoenix', 'https://www.discounttire.com/store/az/scottsdale/s/1284?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.swirlscupcakes.ca/', 'https://www.bestwestern.com/en_US/book/hotel-rooms.50061.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:50061', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, None, 'http://www.americanlaser.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=paid+search&BannerID=4772', 'http://tix4tonight.com', 'http://charlotteyoga.com/', '1592444288', 'http://leopoldstavern.com/locations/#calgary-beltline', 'http://www.hollywoodcarsmuseum.com', 'http://bloomingnails.net', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.championwindow.com/Madison/?lpc=UU-OD-Madison-Yelp&source=ol-yel01&utm_source=yelp&utm_medium=local&utm_campaign=Madison', None, 'http://www.greatclips.com/', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.arizona-chiropractic.com', 'https://heroburgers.com/locations/highway-27-langstaff/', 'https://mtiaz.net', 'http://www.sprinklerdetective.com/home.html', 'http://bajabargrill.com/', '1592444328', 'http://www.kibosushi.com/locations', None, 'https://www.lyft.com/download?utm_source=yelp&utm_campaign=passenger_charlotte_display_inapp_all', 'https://pilotflyingj.com/stores/4', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89128/027192/', 'http://bmwofchampaign.com', 'https://www.petpalaceresort.com/locations/pet-palace-charlotte/', 'http://www.shopjustice.com', 'http://www.cleanjuice.com', 'http://www.sondelfamilyveterinaryclinic.com', None, 'http://www.thecatandcrowonline.com/', 'http://www.wincofoods.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.foxtailfloral.net', None, None, 'http://www.yogurt-ranch.com', None, 'http://www.superstarcarwashaz.com/fullservice.php', 'http://monarchbrewingco.com', None, 'http://www.myplatinumday.com/c', None, None, 'http://www.ebfitnessclub.com/index.html', None, None, 'https://www.amazinglashstudio.com/studios/az/phoenix/phoenix-arcadia', 'http://www.navayogreekbistro.com', '1592444399', 'http://www.palmapasta.com', 'https://www.thegaragedoorheroes.com', 'https://www.movers-clevelandoh.com', None, 'http://lifescapepremier.com', 'https://www.rhpl.ca/node/119', 'https://cobblestone.com/?utm_source=yelp%C3%8A', 'https://www.thetenspot.com/roncesvalles', '1592444420', 'http://www.yardsatnodaapts.com/', None, 'http://kindexchange.ca/', 'http://www.amandalinas.com', 'https://www.josbank.com/store-locator/monroeville-pa-781?utm_source=yelp&utm_medium=listing&utm_content=781&utm_campaign=PA', None, None, 'https://eyetique.com/squirrel-hill', 'http://aqualungvapor.com', 'http://www.autoimagepitt.com/', None, 'http://www.bijinskincare.com', 'https://www.fedoralegalservices.com', None, 'http://www.thesimplegreek.com/', 'http://foreversmilesdental.org', 'http://www.oasiscounselingtoday.com/spring-valley.html', None, 'https://www.fastaffordableair.com', None, 'http://www.hojo.com/hotels/hotel-overview?hotel_id=45510&tel=18008899735&wid=fe:hj:20160201:yl:pp:hjus:45510', 'https://www.boxerproperty.com/office-space/phoenix/11225-north-28th-drive', None, 'http://www.cuparkside.com', 'http://www.crossfitio.com', 'http://www.kellyos.com/', 'http://www.mango.com', 'https://www.tomshouseofpizza.com', 'https://www.cubesmart.com/nevada-self-storage/las-vegas-self-storage/90.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', None, 'http://fishersamericantavern.com', None, None, 'http://www.villamadina.com', None, None, None, None, 'http://www.thebirthdaysuit.com', None, 'http://www.bahamabucks.com/', 'http://www.ebacafe.com', 'http://www.chartreuserestaurant.com/longchamps.html', None, 'http://brimhalleyecenter.com', None, 'http://www.huntersvillegrooming.com', None, 'http://www.speedtheory.ca/cgy', 'http://www.camcorplumbing.com', 'http://www.tutortime.com/your-local-school/cave-creek-az-6074/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://pittsburghsouthside.house.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_pitxs_en_homepage_desktop&code=YB', 'https://ad.doubleclick.net/ddm/clk/434273602;236814625;d', 'https://pinstripes.com/cleveland-ohio', 'http://www.flooringwindowfashions.com', 'http://www.harborfreight.com', 'http://selbergelectric.com', None, 'http://www.purplepenguinsnow.com/', None, None, 'http://www.ribbonsteahouse.com', None, 'http://www.cuttingedgepaintershome.com', 'http://gtgaragedoorrepair.com', 'https://www.olivegarden.com/locations/az/surprise/surprise/1627?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:surprise-az-1627_pl:locurl_rd:1488', None, 'http://www.chillspotlv.com', 'https://www.smallmangalley.org/bars/coffee-espresso/', 'http://www.kellyhawkins.com', 'http://www.mauiwowi.com', None, 'https://www.thehomerwarehouse.com', 'http://www.waunakeevetclinic.com/', 'http://www.valleyrehabltd.com', 'http://www.liaofitaly.com', None, 'http://www.eurekagrill.com', None, 'http://Www.colorfulkreations.com', 'https://www.acarpetcleaninglasvegas.com', 'http://www.vertigotheatre.com', None, 'http://www.blackbearespresso.ca', 'http://www.redrockcanyonlv.org', None, 'http://filmplus.ca/', None, None, 'https://www.enterprise.com/en/car-rental/locations/us/oh/chagrin-falls-highway-auto-center-3919.html?mcid=iyp:8368400', 'https://www.publicstorage.com/arizona/self-storage-phoenix-az/85027-self-storage/1113?pid=wyelp&CID=1245&CHID=AFL', 'https://bestlilframeshop.com', 'http://www.jeffreywhite.com', 'https://www.discounttire.com/store/az/glendale/s/1016?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', None, 'http://www.cavalia.net/en/odysseo/tickets-info/toronto-can', 'https://www.eq3.com/ca/en?utm_source=Yelp&utm_medium=yelphttps://www.eq3.com/ca/en?utm_source=Yelp&utm_medium=yelphttps://www.eq3.com/ca/fr?utm_source=Yelp&utm_medium=yelp&src_id=CHL40SCL012-ACT0007-Undf-INT0000', 'http://www.clevelandhardwoodrestoration.com', '1592444641', 'http://yourspacesalons.ca/natural-solutions', 'https://www.flooranddecor.com/store?StoreID=120', None, 'http://blacknbluerockstar.com', '1592444653', 'https://www.higleydentalcare.com', None, None, None, 'http://www.egotsk.com', 'https://carle.org/locations/carle-foundation-hospital', 'http://www.leisureindustries.ca/', 'http://www.fremontcountryclubvegas.com/', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'http://www.nannyexchange.com', 'https://www.a1furniture.com', 'http://www.potbellypanda.com', 'http://www.polishroom.com', 'http://aimsforwellness.com', 'http://www.ci.wesley-chapel.nc.us/index.asp?SEC=AB5555F0-565F-44F6-8C1C-EEF492AD0F45&Type=B_BASIC', 'http://paragliderrides.com/', 'https://www.maaco.com/locations/wi/madison-11856/', 'http://finedreadlocs.com', None, None, 'http://www.mercedesbenzcalgary.com/service/index.htm', 'http://www.castsalonandspa.com', None, 'http://www.originalbreakfasthouse.com', 'http://www.vivobeautybar.com', 'http://www.starbucks.ca', 'http://www.pittsburghmoldremediation.net', 'http://www.cashmanphoto.com', 'http://apricotlaneboutique.com/strongsville', 'http://www.pacini.ca', None, 'http://www.johnkootdmd.com', 'http://www.doralfiremesa.org/', 'http://www.genesrv.com', 'http://www.reynoldsteeth.com', 'http://www.sozafitnessandwellness.com', 'http://www.samwinter.net?cmpid=cffx_blm_0006', 'https://www.thomasslonakerofficial.com', None, '1592444748', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.jellysgaragedoors.com', 'http://www.swirlscupcakes.ca/', None, 'https://karatechandleraz.com', 'http://www.sergeswigs.com/', 'http://tryexoticcars.com', 'http://www.hollyhairdesign.com', 'http://www.alikatphotography.com', 'http://www.tuscaroracc.com', 'http://www.fellysflowers.com', None, None, None, 'https://www.enterprise.ca/en/car-rental/locations/canada/on/scarborough-eglinton-square-c261.html?mcid=iyp:8368400', 'http://www.kiss-salon.com', 'http://www.abcdentalcare.com', 'http://www.stonecrestfamilydentistry.com', 'http://www.sonicdrivein.com/', 'http://www.headfoneshop.com', None, 'https://puls.com/?utm_campaign=site&utm_medium=cpc&utm_source=ylp', 'http://www.thegrindaz.com', None, 'http://www.budgetbuysmart.com', 'http://www.audioexpress.com', 'http://www.johnnyonthespotrooter.com/', 'http://www.lasvegascolorprinting.com', None, 'http://www.dumplinggirls.com', 'http://www.freshpizzaplus.ca', 'http://www.cravetap.com', None, 'http://oakvilleshops.com/stores/china-chopsticks-oakville/', 'http://www.thathawaiianguysbbq.com', 'http://www.patcatans.com/craft-store-locations/parma-oh', 'http://www.thecheesesteakjointaz.com', None, 'http://www.jandshomeinspections.com/', 'http://www.masseria.ca', None, 'http://mfgym.net', 'http://www.yves-rocher.com', 'http://www.kaleidoscopejuice.com/', None, 'http://oasistreescorp.com', None, 'http://www.sushikampai.com/', 'http://www.hobbylobby.com/StoreDetail/500', None, 'https://www.unyozi.ca', 'http://www.littlecaesars.com', 'https://www.axispest702.com', 'http://www.kivcc.org', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://kafeteriacleveland.com/', None, 'https://www.usps.com/', 'https://www.theoakwoodhardware.com', 'http://www.stoutirishpub.ca', 'http://www.mypoolbutler.com', 'https://vpscheap.net', None, '1592444898', '1592444901', 'https://www.famousfootwear.com/?partnerid=YELP', None, 'http://www.stonecliffepa.com', 'http://www.envypmu.com', '1592444912', 'https://locations.timhortons.com/ca/on/richmond-hill/1070-major-mackenzie-dr.html', 'https://www.eyecareaboutvegas.com', 'http://salondushons.com/', 'http://www.alavieillecheminee.com', 'https://www.kohls.com/stores/oh/mentor-237.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.marcos.com', 'http://riceshopvegas.com', 'http://www.miragefiberarts.com', 'http://www.jpcharlotte.com/soco-bar', 'http://www.djsfishandchips.com/', None, None, None, 'http://www.AZBrian.com', '1592444946', 'http://azmedicalcare.com', '1592444951', 'https://www.tourdetavern.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.fortmillpharmacy.com', 'http://www.advancedeyecare.com', None, 'http://www.redcranberries.ca/', '1592444967', 'http://www.noblebeastbeer.com', 'http://www.vinapizza.com', 'http://hudsonscanadaspub.com/location/crowfoot', 'http://laughingbuddhaaz.com', 'http://www.trainingroomfitness.ca/', '1592444982', 'http://www.bathandbodyworks.com', 'http://www.regishairstylists.com', 'http://meineke.com', None, 'https://azvent.com/locations/chandler.php', 'http://www.prepandpastry.com/locations/scottsdale/', 'http://www.konareefaz.com', None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=891&utm_content=bpas', 'http://goldfingerslasvegas.com/', None, None, None, None, 'http://oldcitysoda.com', None, None, 'http://a2autorepair.com', '1592445022', 'https://www.phoenixnewtimes.com', 'http://www.anoziralandscape.com', 'http://www.itamaesushi.ca/', 'https://www.chastainlegalgroup.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.nofrills.ca/store-locator/Nick+%26+Mira%27s+NoFrills+North+York/3136?storeId=3136', 'http://www.karamia.ca/main.html', None, 'http://www.psychandpsych.com', 'http://www.anylabtestnow.com/franchises/chandler-85224/', 'http://www.ultimatepoolservices.com', 'http://www.madridcourtyard.com', None, 'https://www.portillos.com/locations/avondale/', None, 'http://www.piratelife.ca/', 'http://www.peoriacosmeticsurgery.com/', None, 'http://www.owlcleaners.com', None, 'http://www.keyrealtyschool.com/', None, 'http://www.salsanaiboa.com', None, None, 'http://www.uptownwindowphx.com', None, 'http://www.blackbirdbaking.com', 'http://www.shamrockautocare.com', None, 'http://www.jaipurexpress.ca', None, None, None, 'http://proofyyc.com', 'http://www.banfield.com/veterinarians/wi/madison/emn?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, 'http://www.greatclips.com', '1592445103', 'http://www.wendelclarks.com/', None, 'https://www.wellsfargo.com', 'http://www.redmangousa.com', 'http://www.billgrayvolvo.com', 'http://www.agentwhitmore.com', 'http://enticelounge.com', 'https://americannatural.com', None, 'http://www.pizzalotto.com', 'http://www.firehousesubs.com/?ref=yelp', None, 'http://www.thecaledonian.ca', 'https://www.camdenliving.com/charlotte-nc-apartments/camden-gallery', 'http://www.skinjectables.ca', 'http://dotssouthernkitchen2.com/', 'http://www.superior-tire.com', None, 'http://headshotslasvegas.com', 'http://www.russoandsteele.com', 'https://www.empiretoday.com', None, 'http://www.biltmoreent.com', None, 'http://www.absolutetherapymassage.com', 'http://Www.Sugarnail.us', None, 'http://www.3margaritasaz.com', None, 'http://www.portuguesechicken.ca', 'http://locations.michaels.com/NV/NORTH-LAS-VEGAS/9195/', None, 'http://killerqbbq.com', 'http://www.fullracemotorsports.com', None, 'http://eaglesnestgolf.com', 'http://www.express.com', None, 'http://www.springviewhhc.com/', 'http://www.thelovestore.com', 'https://yardcookeddishes.business.site', 'http://www.rock-a-bye.com', 'http://www.follybrewing.com', None, None, 'https://mountainview-hospital.com/service/er-at-aliante', 'http://www.naakitifloraldesign.com', 'https://myextraordinarysmile.com', 'https://www.silverstateortho.com', 'http://gabbys.ca', 'https://brodflour.com', '1592445224', 'https://www.plasticsurgeryvegas.com', None, None, 'http://www.davidvelascodds.com/', 'http://www.house-maison.ca/', None, 'http://www.khavkinclinic.com', 'http://www.vestispgh.com', 'http://www.iniziosalonscottsdale.com', 'http://www.bareradiancelv.com', 'http://www.HappyGrillMadison.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'https://www.allnevadainsurance.com', 'http://popeyes.com', 'http://salazarsdetailingservice.com', 'https://greenvalleyranch.sclv.com/Entertainment/Lounges-and-Bars?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', None, 'https://www.loschicosvaughan.com', 'http://www.richteraleworks.com', 'http://orthosportlasvegas.com/locations/henderson/', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'http://alphillipslv.com/', 'https://www.wernerjewelers.com', None, None, 'http://www.hapaizakaya.com', 'https://www.panerabread.com/en-us/home.html', 'http://graphicka.com/', '1592445289', 'http://eastgilbertfootandankle.com', None, 'http://www.lubecity.com/locations.html', 'https://www.walgreens.com/locator/walgreens-6649+morrison+blvd-charlotte-nc-28211/id=1376', None, None, 'http://grannynannies.com/phoenix', None, 'https://www.jiffylube.com/locations/az/peoria/659', 'http://www.sushishop.com/', 'http://www.oximedical.com', 'https://www.dillards.com/stores/the-meadows-mall-las-vegas-nevada/0503', 'https://www.desertdiamondhvac.com', 'http://www.mollybglutenfree.com', None, 'http://kellyclark.com', 'http://www.gentledentalmillavenue.com/', 'http://www.pizzanova.com', 'http://www.invacare.com', 'https://locations.arbys.com/us/il/rantoul/760-w-champaign-st.html', 'http://www.EstatesOnMaryland.com', None, 'http://www.npdelivered.com', 'http://www.theparkingspot.com', 'http://graciousliving.com/products.php', 'https://phantasycleveland.com', 'http://www.intownsuites.com/locations/charlotte-northeast-chn/', None, 'https://dychespropertyservice.com', 'http://www.PiccolisPets.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006435131063&ds_s_kwgid=58700000444951711&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'https://www.greentreeboro.com/parks.php', 'http://toasties.ca', 'http://www.restaurantlastrada.ca', 'http://www.patagonia.com/patagonia-pittsburgh-5509-walnut-st-pittsburgh-pa-15232/store_1504720107.html', 'http://www.bedo.ca', None, 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', 'http://local.dmv.org/north-carolina/gaston-county/mount-holly/785-w-charlotte-avenue/dmv-office-locations.php', None, 'https://www.fastmed.com/urgent-care-centers/gilbert-az-walk-in-clinic-east-williams-field-road/?utm_campaign=BizURL&utm_source=Yelp&utm_term=YelpOrganicListing', 'http://www.benfranklinplumbingcharlotte.com', 'http://baharsalon.ca/', 'http://www.acerentacar.com/landing/Nevada/Las-Vegas/Las-Vegas-Intl-Airport.aspx', 'http://www.mazdaofsouthcharlotte.com/?utm_source=yelp&utm_medium=business_url&utm_campaign=local-citations', 'http://www.carolinasgo.com/', 'http://www.tattoofaction.com', 'https://www.liquordepot.ca/Our-Stores/ctl/MobileStoreDetails/mid/440/storeID/140', None, 'http://www.canvasclubboxing.com', None, 'http://www.lifelinescreening.com/?sourcecd=WLNV001?utm_source=Yelp&utm_medium=profile&utm_campaign=Yelp', None, None, 'http://www.trolleypub.com/charlotte', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.kegsteakhouse.com/locations/mississauga-northwest-keg/', 'http://www.moxiehairstudios.com', 'http://rosecustomcollision.com', '1592445424', 'http://crownstationpub.com', 'http://www.medicalcarenowlv.com', None, None, None, 'https://www.dominos.com', None, None, '1592445446', 'http://www.uptownpremierdental.com/services.htm', None, 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=1', None, None, 'http://www.hoflandlaw.com', 'http://surgical-dermatology.com', None, None, 'https://www.scefcu.org', 'http://www.oldbarberhouse.com/', None, 'http://www.bk.com/restaurants/ca/lakewood/2438-east-carson-street-10722.html', None, 'http://gamechangerssportslv.com', None, 'https://www.sunsetgrill.ca', 'http://www.balzacs.com/locations/ryerson-image-arts/', 'http://www.thenewsweetindulgence.biz', 'http://www.blunotes.com', 'http://www.contest-sundance-vacations.com', None, 'http://starrick.com/', 'http://www.greatclips.com', 'http://peterpiperpizza.com/', 'http://www.bertoluccibraziliansteakhouse.com', 'http://danishpastryhouse.ca', 'http://rgriegomd.com', 'http://www.casareynosochandler.com/', 'http://www.youmoveme.com/ca/calgary-movers', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.costco.ca/warehouselocatordetailsview?langId=-24&storeId=10302&catalogId=11201&warehousenumber=1076&beginaddress=calgary&numofwarehousestoreturn=null&location=calgary&callingpage=warehouselocatorview', 'http://www.layersbakery.com/', 'http://www.midas.com/toronto/store.aspx?shopnum=9194&dmanum=857001', 'http://www.arizonasinus.com', 'http://www.mccarran.com/', 'http://www.pier1.com', 'http://www.searsauto.com/stores/6701', None, 'http://sincitysnowboards.com', 'http://www.facialcosmeticsurgery.ca/', None, 'http://www.lvairductcare.com', None, None, None, None, 'http://houseofsmokeslv.com', None, 'http://www.woodsidesquare.com', 'http://topnailslasvegas.com', 'http://local.fedex.com/pa/west-mifflin/office-0532/', 'https://www.airporttravellersinn.com', None, None, 'http://sammysdelirestaurantscharlotte.yummybistro.xyz', None, 'http://www.pizzahut.com/', 'http://www.bideliasbead.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.mikebassford.net', None, 'http://www.fuddruckers.com', 'http://www.danaplayground.com', 'http://www.grunos.com', '1592445605', 'https://www.forever21.com/ca/', 'http://www.streetsalon.ca', 'https://aplusplumbingservice.com', 'https://www.londongold.com/company/locations/arrowhead/', 'http://www.1213studio.com', None, 'http://www.luminessspa.com', 'http://scala20.com/fr', 'http://www.dominos.com', 'http://www.travelproluggageoutlet.com/', 'https://www.illumi.com', None, None, 'http://www.champaignclinic.com', 'https://www.target.com/sl/las-vegas-blue-diamond/2164', None, 'http://azice.com/gilbert/', 'http://sugaringlv.com', 'http://www.onemedical.com/phx/doctors?utm_medium=referral&utm_source=yelp.com&utm_campaign=sitelink', 'http://buttercupbeauty.co', 'http://www.bbqgrillsgonewild.com', 'http://sushiculiacan.com', None, 'http://memphisonmain.com/', 'http://www.kwikkill.net', 'http://www.persemobile.com', 'http://www.giftedhandsgifts.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.abodyinbalancelv.com', 'https://ayurvedarituals.ca', 'https://www.wellsfargo.com', None, 'https://www.thirdfederal.com?=ad.doubleclick.net/ddm/clk/458420725;262568795;w', 'http://www.finishline.com', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/north-toronto-eglington-yonge-c245.html?mcid=iyp:8368400', 'http://www.krispykreme.com', 'http://www.custompowdercoatnv.com', 'http://fcrsolutions.net', 'http://www.autoglassbuddy.com', 'https://www.dentalartsofchandler.com', None, 'http://www.dondonchineserestaurant.com', None, None, None, 'http://www.lilbuddyspopcorn.com/index.html', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://davidrosssalon.com', 'https://www.jiffylubeontario.com/markham-5706-highway-7/', 'http://mrspatio.com', 'https://www.avanaatthepointe.com', 'https://athleta.gap.com/stores/pa/pittsburgh/athleta-7076.html', 'http://www.phdhomesolutions.com', 'http://freshstartwellnessaz.com', None, 'http://www.atrias.com', 'http://www.allthebestcatering.com', 'http://www.riversquareanimalhospital.com', 'http://clubtattoo.com', None, 'http://www.tavernrestaurantgroup.com', 'https://www.mypetmarket.com', 'https://locations.jackinthebox.com/us/az/peoria/8236-w-deer-valley-rd', 'http://odilechocolat.com', None, 'http://www.lacentre.com', 'http://www.sweetgirlcookies.com', None, 'http://www.monacreations.com', None, 'http://www.villageinn.com/locations/110695', None, 'http://fourpawsdogretreat.com', 'http://www.spinnerspizza.net', None, 'http://www.turfhub.com', 'http://www.clarkcountynv.gov/Events/Pages/default.aspx', None, 'http://sterlinginterstate.com', 'http://www.arizonafacialplastics.com', 'http://www.maxieslv.com', 'http://www.murphystaproom.com', 'http://www.parmamarine.com', None, 'https://moxies.com/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', None, '1592445798', 'http://tfyogurt.ca', 'http://cafetal.coffee', 'https://www.hilton.com/en/hotels/lasnohx-hampton-las-vegas-north-speedway/?SEO_id=YELP-HP-LASNOHX', 'http://local.skechers.com/AZ/GOODYEAR/223/', 'http://www.optimabiltmore.com', None, 'http://lewinkstudio.com', None, 'http://foxspizzacarnegie.com', 'http://www.lexusofmadison.com', '1592445826', 'http://gingerrootrestaurant.com/', None, None, 'http://legendsbarchampaign.com', None, 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', 'http://www.eurotransportintl.com', 'http://www.cbac.com/concord?utm_source=Social&utm_medium=Yelp', None, 'http://www.daysinncalgary.ca', None, None, 'http://www.searsoptical.com', 'http://stephanierider.com', 'https://www.capriottis.com', 'https://www.target.com/sl/north-scottsdale/936', 'https://haircutmenhigleygilbertaz.com', 'https://www.ulta.com/stores/solon-oh-573', 'http://www.icing.com/pws/StoreFinder.ice?country=US&storeId=228&findStore=true', None, None, None, 'http://www.merchantsofgreencoffee.com', 'https://ad.doubleclick.net/ddm/clk/434328053;236814625;e', 'http://www.thenewmri.com', None, 'https://www.anthropologie.com/anthro/store-locator/store/las-vegas/fashion-show-mall/00461?currency=100003#/detail?storeId=00461', 'http://www.morrisonpoolnspaservices.com', 'http://www.netcomlearning.com/aboutnetcom/vegas_bootcamp.phtml', 'http://www.jademountainteas.com', None, None, 'http://www.regalnails.com', 'http://www.alwaysperfectionsalon.com', 'http://www.khavkinclinic.com', None, 'http://www.starbucks.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.azlaserclinic.net/', None, None, None, 'http://AZFirearms.com', 'http://www.signaturerugsnv.com/', 'http://grungygalz.com', 'http://www.kidspluspediatrics.com', 'https://www.mkdalexander.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://usonv.com', None, 'http://www.zpizza.com', 'http://allstarservicesandrepair.com', 'http://www.completelycleanaz.com', 'http://www.patatepersil.com', 'http://www.signanddrivecars.com', None, 'https://www.untuckit.com/blogs/store-locations/scottsdale', None, 'http://www.michaelshairstudio.ca/', 'http://www.salonscavo.com', 'http://plopools.com/', 'http://www.wingstop.com', 'https://www.wyndhamhotels.com/hotel/29414?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:29414', None, None, 'http://wingsup.com', 'https://www.capellibayviewvillage.com', 'http://www.swisschalet.com', 'https://foodbyfabio.com', None, 'https://www.seniorplanning.org', 'http://www.bulwarkpestcontrol.com/', None, 'http://cakesbyrobertthebeach.com', 'http://riseshinecafe.com/', None, 'https://www.cosmopolitanlasvegas.com/lounges-bars/vesper-bar?utm_source=yelp&utm_medium=organic&utm_campaign=yelp', '1592445997', '1592445999', None, 'http://www.clubproae.com', None, 'http://www.timhortons.com/ca/en', None, 'http://www.chavezlawncare.com', 'http://highnoontattoo.com', 'http://www.shredarizona.com', 'https://www.awesomesaucebowls.com', 'http://www.courtesychev.com', 'http://akronricebowl.com/', 'http://www.firstofficiant.com', 'https://www.theskincentermd.com/cosmetic-plastic-surgery-shadyside-pittsburgh-pa', None, None, 'http://www.quick-kleen.com', 'https://www.jacksoncomfort.com', 'http://manuellatruwe.com/', None, 'http://www.sushirun.ca', 'http://www.sleepnumber.com/?utm_source=Yelp&utm_medium=CPC&utm_term=CTA&utm_campaign=N_r4lWWL8uTgc02nZZkydA&cm_mmc=Yelp-_-Yelp-_-WebsiteLink-_-N_r4lWWL8uTgc02nZZkydA-904825&tag=904825', 'http://www.artistsupplies.com/store/index.php', None, None, 'http://inkandtoneraz.com', 'http://findlayhonda.com', None, None, 'http://www.sushishop.com/fr', 'http://www.nailsocietylv.com', None, 'http://www.charlottehomeinspector.com', 'http://fixauto.com/calgary-coachworks-north', 'http://www.kinglibertyhealthcentre.com/', 'http://rockypointscubadive.com', 'http://www.secureselfstorage.ca/ontario-self-storage/mississauga-l4x-0a2/', 'http://www.terribleherbst.com/', 'https://fabutan.com/locations/ontario/etobicoke/queensway/', 'http://www.italianvillagepizza.com/', 'http://explore.calvinklein.com/en_US/explore/ckperformance', 'https://www.orangetheory.com/en-us/locations/ohio/solon/6025-kruse-drive/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.starbucks.com/store/10759/', 'https://www.dunfieldphysio.com', 'http://www.pourbeer.ca', None, 'http://www.americanapparel.net/StoreLocations/Details.aspx?RetailStoreID=78&utm_source=yelp&utm_medium=link&utm_term=tempe&utm_campaign=store_pages', None, 'http://www.dollartree.com', 'http://www.arsenalciderhouse.com/', None, 'http://www.larrymillerchryslerjeepavondale.com/service/index.htm', 'https://www.challengerschool.com/campus/nevada/las-vegas/los-prados', 'http://www.raysmtb.com/cle/index.php', 'http://goldennationalcalgary.ca', 'http://www.worldsgreatestrockshow.com', 'http://colonicsbyannabella.com/', None, '1592446128', 'http://www.bulldogbeerandwine.com', 'http://www.dutchdreams.ca', 'http://www.thelazydaisycafe.com', 'http://www.retrobakerylv.com', None, 'http://www.sugarmewax.com/peoria/', 'http://arizonamanualtherapycenters.com', None, 'http://www.origins.com', 'http://eatdannyspizza.com', 'https://superstitionnailsspamesa.com', 'http://www.tuttifruttikensington.com', 'https://www.goingupgaragedoors.com', 'http://www.valvistalakes.org', 'https://ashleyhomestore.ca/pages/richmond-hill', 'http://www.uptownpower.com/', 'https://www.harveys.ca', None, None, 'http://www.azclc.com', 'http://www.liveatmiramonte.com', 'http://www.petrackplumbing.com', 'http://www.smcauto.com/', '1592446181', '1592446183', 'http://www.prisonbreaker.ca', 'http://www.sunwestfcu.org', 'http://www.foglie.ca', 'http://www.azequine.com', 'https://locations.captainds.com/ll/US/NC/Matthews/9715-E-Independence-Blvd', 'https://www.kimptonsaintgeorge.com', 'http://www.maddogsportsbar.com/home-mesa.html', 'http://www.case.edu/diningservices/diner.htm', 'https://www.get-go.com/', 'http://www.hybrid-autorepair.com', 'https://www.stratospherehookah.com', None, 'http://www.benchmarkschool.net', 'http://www.azcentralcu.org/home/arizona-locations/chandler-az-branch', None, 'http://www.pnc.com', 'http://www.fitzgeralds.ca', None, 'http://elencantorestaurants.com', 'http://www.taverncharlotte.com', 'http://www.casting-entertainment.com', 'http://www.firkinpubs.com/drakeandfirkin/', None, None, 'http://www.kareliakitchen.com', None, '1592446242', 'http://ecowashlv.com', 'http://www.culvers.com/restaurants/chandler-az-s-arizona-rd', 'http://www.thedetoxmarket.ca', 'http://woodlandtoyota.ca', 'http://www.senormist.com', 'http://www.thekingswayanimalhospital.com', None, 'https://www.walmart.ca/en/stores-near-me/westbrook-store-3009', 'http://www.valentinossmokinsalmon.com', 'http://www.tatyana.com', None, 'http://www.paradisebakery.com', 'https://salon84az.com', None, 'http://www.altanissan.com', 'http://www.savethismemory.com', 'http://www.southhillsbrewing.com', 'http://www.mycenters.com/oral-facial-surgery/contact-us/lake-norman-office-map.html', 'http://www.saloncentric.com', 'https://www.ubreakifix.com/locations/scottsdale', 'http://www.michaelkors.com', None, None, '1592446294', 'https://stores.bestbuy.com/az/gilbert/2288-e-williams-field-rd-1189.html/?loc=ns100&ref=NS', 'http://www.outback.com/locations/wi/madison-junction', '1592446301', '1592446304', 'http://www.wilgroveairport.net/', None, 'http://www.springmountaindental.com', 'http://www.dunkindonuts.com', 'http://www.interchangelounge.com', 'http://www.hensonvillage.com', 'https://friendlydentalgroup.com/locations/matthews/', None, 'http://www.wethedjs.com', 'http://www.signaturewaste.com', None, 'http://www.terribleherbst.com/', 'http://triplerchildcarearizona.com', 'http://johnnyrockets.com', 'https://www.85cbakerycafe.com', 'http://www.phoenix.edu', None, 'http://www.thepearlatstrose.com', 'http://www.pokerstattooparlor.com/', 'https://mrsweetspastries.com', 'http://www.goodwill.vegas/thrift-store-68-4580-west-sahara-avenue-las-vegas-nv-89102/', 'http://www.cineplex.com/Theatre/cineplex-cinemas-vaughan', None, 'http://www.clpgh.org', None, 'https://www.avillameadows.com', None, None, 'http://ebonylmt.wixsite.com/renewedspiritmassage', 'http://www.extremepita.com/', None, 'http://DallasAndrews.com', None, 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', 'https://modpizza.com/locations/metrocenter/?utm_source=yelp&utm_medium=referral&utm_campaign=yelplistingbusiness', None, None, None, None, '1592446389', None, 'http://www.fuzionhairdesign.com', 'http://clintondental.ca', 'http://www.desertwolfair.com', '1592446398', 'http://www.teamsiok.com', 'http://www.harkinstheatres.com', None, 'http://www.pizzapizza.ca', 'https://www.silveradoranchdentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, None, 'http://www.choicerespiratorycare.com', 'http://www.ozbarphx.com/', 'http://medpost.com/location/laveen-az', 'http://www.harrahs.com/casinos/caesars-palace/casino-misc/seahorse-lounge-detail.html', 'http://crushsalonlv.com', 'http://www.legacy-village.com', None, 'https://locations.vitaminshoppe.com/az/mesa/vitamins-supplements-mesa-az-466.html', None, 'http://www.blasiolespizza.com', 'http://travertinepowerclean.com/index.php', 'https://paintingco.com/nevada', 'http://www.arbys.com', 'http://eatbystaceyweber.com', 'http://www.starsofhorsemanship.com', 'http://www.sprengerhealthcare.com/communities/amherst-manor-retirement-community/', 'http://wondroushair.com', 'https://ca-stores.casper.com/casper-toronto-premium-outlets-39932718b8b4', 'https://www.jetblue.com', 'http://www.ihg.com/crowneplaza/hotels/us/en/charlotte/cltcp/hoteldetail', 'http://www.zoenailsatayrsley.com', None, 'http://justenergyentertainment.com', None, '1592446474', 'http://www.zestnaturalmedicine.com', 'https://ecoelectriclv.com', None, 'https://campbellssweets.com/locations/campbells-sweets-factory-ohio-city/', None, None, 'http://www.warehousegroup.ca/saint-laurent-warehouse', 'http://azpipedoctor.com', 'https://www.sepainandspinecare.com/morehead.html', '1592446497', 'https://www.lelabofragrances.ca', None, 'http://www.buffalowildwings.com', 'http://www.storagedepotlasvegas.com/', 'http://www.divinossportsbar.com', 'http://ExtremeSmiles.com', 'http://www.serviceking.com/locations/service-king-north-rancho-drive?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', None, None, 'http://www.dragonboatcharlotte.com', 'http://www.pacini.com/en', 'http://www.associatedappliancesales.com', None, 'https://www.sunburstlandscaping.com', None, 'http://www.carpetandflooring.com', None, 'http://sapphirelasvegasclub.com', 'https://www.riteaid.com/store-details?storeNumber=03131', None, None, 'http://www.siegelsuites.com/rent-apartment-las-vegas/cambridge-las-vegas-apartments.php', 'http://www.southcentremall.com', 'http://www.connellystores.com', 'http://www.quickclaimusa.com', 'http://www.terribleherbst.com/', 'http://www.littlecaesars.com', '1592446555', 'https://www.hilton.com/en/hotels/phxrmgi-hilton-garden-inn-surprise-phoenix/?SEO_id=YELP-GI-PHXRMGI', '1592446561', None, 'http://www.mothershipcoffee.com', None, 'https://haircutmengreenvalleyhendersonnv.com', '1592446573', '1592446575', None, None, 'http://www.vegasbaby4dultrasound.com', '1592446583', 'https://www.dronesplus.ca', None, 'http://syshair.com', '1592446592', None, 'https://inspirationmartialarts.com/contact-us/glendale', None, 'https://www.menswearhouse.com/store-locator/4501?utm_source=yelp&utm_medium=listing&utm_content=4501&utm_campaign=PA', 'https://www.metropcs.com', '1592446606', None, None, 'http://www.firstdraftbookbar.com', None, 'https://www.precisioncorporation.com', '1592446619', 'http://arrivadental.ca', 'http://www.frysfood.com', 'http://www.mybluesteelteam.com', 'http://taraophotos.com', 'http://goldsgymbeaconsfield.com', 'http://batteriesforless.weebly.com', 'http://www.hauntedAZ.com/', None, 'http://www.allianceia.com', 'http://www.premierwheelsdirect.com', 'http://www.pinkaow.com', '1592446648', 'http://www.gilbertglass.com', None, 'http://wecarefwc.com/', None, 'http://www.thefreshmarket.com/', 'https://stores.petco.com/az/mesa/pet-supplies-mesa-az-1119.html', 'http://www.1027thecoyote.com', None, None, 'http://www.skindeepmedispa.com', None, 'http://www.highlandautobodyandcollision.com', None, None, 'http://www.premierparadise.net', 'http://clubtanningmesa.com', None, None, 'http://www.bytesburgers.com', 'https://www.foxwildlifeaz.com', None, 'http://www.meineke.com/store/matthews-1000', 'https://www.tireshoppittsburgh.com', 'http://yogalutionstudio.com/', 'http://www.southhillselectric.com', 'http://www.styleseat.com/lynnettesimmons', 'http://www.odslimo.com/', 'http://www.ccculv.org', '1592446712', None, 'https://www1.shoppersdrugmart.ca', None, None, 'http://www.curvaliciousclothes.com', 'http://www.nadiasrestaurant.com', 'http://superiorcustomcabinetsllc.com/', 'https://www.livecerulean.com/arctic-cryotherapy/', None, '1592446737', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.champssports.com', 'http://watchit.ca', 'http://www.paradisebakery.com/', 'http://www.letsgrowstudio.com', None, 'http://www.bayviewvillageshops.com', 'http://thaspotbbq.com/', 'https://www.officedepot.com/storelocator/az/phoenix/officemax-6319/', '1592446772', None, 'http://www.eatmorefellinis.com', 'http://bigsmokeburger.com/single-location/?id=1965#locations', 'http://www.best-storage.com', 'http://www.erikastylist.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCES', 'https://www.supercuts.com/locations/on/north-york/york-mills-square-haircuts-5743.html', 'http://www.prettyphenomenalphoto.com', 'http://www.midwestvethospital.com', 'http://www.chimatravel.net', 'http://www.artonbeads.net', 'http://www.jellymoderndoughnuts.com', 'http://www.mrtonkatsu.com/', None, 'http://www.sherryeskitchen.com/', 'http://storelocator.staples.ca/stores/en_CA/ON/Etobicoke/11', 'http://www.acacia-endo.com', 'https://ca.usembassy.gov/embassy-consulates/toronto', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', 'https://www.artisanair.ca', 'http://www.barleysandhops.com', None, 'http://www.azroofandpaint.com', 'http://crumblcookies.com', 'http://www.aesirmetalwyrks.com', 'http://buildapastaonline.com', None, 'http://www.michelesmedspa.com', 'http://www.albanypizza.ca', 'http://phoenixindoorautosales.com/', 'http://halton.cpcc.edu/', None, 'http://www.usps.com', 'https://order.subway.com/Default.aspx', 'https://carolinapinesplumbing.com', None, 'https://www.fastmed.com/urgent-care-centers/phoenix-az-walk-in-clinic-maryvale-parkway/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.rossocoffeeroasters.com', 'https://www.seniorlifestyle.com/property/arizona/amethyst-gardens/?utm_source=yelp&utm_medium=Business%20URL', None, None, 'http://www.myfirstchoicecatering.com', 'http://www.swanrehab.com', 'http://www.FurnitureMattressDirect.ca', 'http://www.dependable-locksmith.com', 'http://restaurantfulam.com/page.php?id=25', 'https://www.mandalaybay.com/en/amenities/beach.html', 'http://slslasvegas.com/venue/beach-life', '1592446877', None, '1592446882', 'http://www.gianteagle.com', None, 'https://www.ramen123.com', 'http://www.charlotterusse.com', 'https://northvalleyca.org', None, None, None, 'http://www.regalnails.com', 'https://www.lovescyclingandrepairs.com', 'http://www.wovet.com', 'http://www.wetzels.com', '1592446911', 'http://champps.com', None, None, 'http://novetrattoria.com', 'http://www.bravoitalian.com/bravo_eton.html', 'http://www.mcninchhouserestaurant.com', 'http://www.z-teca.com', 'http://panacheinvitations.ca', None, 'http://climbcamelback.com/echo/', None, None, 'http://jlevines.com', None, None, None, 'http://www.acateredaffairlv.com', 'http://www.sonicdrivein.com/', None, None, None, 'http://www.sterlingmagnoliaapartments.com/', 'http://www.thehomeconsignmentcenter.com', 'http://purehealthchiro.com/', None, None, None, 'http://www.parislasvegas.com/casinos/paris-las-vegas/casino-misc', 'http://gholsonvanlines.com', 'https://myrosatis.com/urbana/', 'http://www.fairviewcuisine.com', 'http://www.papajohns.com', None, 'http://www.stepsdancestudio.com', '1592487749', 'https://delafontaine.squarespace.com', 'http://www.arrahairsalon.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.sugarspapgh.com', 'https://infernoescaperoom.com', 'http://www.portofsubs.com', None, '1592487776', 'http://www.redrockcanyonlv.org/hikes-trails/white-rock-la-madre-spring-loop', 'http://www.apple.ca', 'http://bellasisalonspa.com', 'http://www.thehowardteam.net', None, 'https://www.wellsfargo.com', None, None, '1592487806', 'http://www.happycanbottledepot.com', 'http://www.gloweventcentre.com', 'https://www.famousfootwear.com/?partnerid=YELP', 'http://www.factoryfinishmobile.com', 'http://www.percenttaphouse.com', 'http://www.gypsycafe.net', 'http://www.theraq.ca', 'http://www.thehiddenpalace.net', 'http://www.truehotyoga.com', 'http://www.delsolbarbers.com', None, 'http://www.diamond-heads.com', 'http://regaldiscountcleaners.com/', 'http://www.stevepurtelldds.com', None, 'http://www.pizzanova.com', 'http://www.alcoveattheislands.com', 'http://www.desertartsupplies.com', 'https://hanasushicafe.com', 'http://lepetit-chocolat.com', 'http://dcfittempe.com', 'http://www.spanx.com/retail-stores', 'http://www.chezcora.com', 'https://www.mattressfirm.com/stores/az/tempe/mattress-stores-tempe-az-85284-8312.html', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.buzz-technical.com', 'http://www.grapesitalianrestaurant.com', 'http://www.ultimateweddingcakes.com', 'http://www.starbucks.com/store/1006086/', 'http://www.travelingmassagetherapy.com', 'http://www.luckylimolv.com/', None, None, 'https://www.petsuppliesplus.com/Store/PA/Bethel-Park/Bethel-Park/87?utm_source=Yelp&utm_medium=Store-Page%C3%8A', "https://www.brueggers.com/?utm_source=yelp&utm_medium=homepage&utm_campaign=strongsville&utm_term=Bruegger's%20Bagels%20Home%20Page", None, 'https://varietynails.business.site', None, 'https://grinders-coffee-co.business.site', 'http://www.jeremymueller.com', 'http://www.shantibaba.ca', 'http://www.aircarolinas.com', 'http://www.vipexpresstransportation.com', 'https://www.wilhelmautomotive.com/locations/chandler/', None, 'https://www.smalv.com/OurCenters/HealthCareCenters/Civic-Center', None, 'http://www.vanitycharlotte.com', None, 'http://arizonaoncology.com', 'https://www.nucarrentals.com/locations/las-vegas_car_rentals.htm', 'https://www.regmovies.com/theatres/regal-stonecrest-at-piper-glen-imax-rpx/0384?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Stonecrest+at+Piper+Glen+4DX,+IMAX+&+RPX', 'http://wisconsinfertility.com', 'http://www.titanautomotive.com', 'http://www.imergencylv.com', None, None, 'http://www.amestile.com', None, 'http://www.tempe.gov/Home/Components/FacilityDirectory/FacilityDirectory/32/3542', 'https://www.calforex.com/en/locations/foreign-exchange-toronto-downtown/', 'http://www.parrish-mcintyre.com', None, None, 'http://www.philthyphillys.com', '1592487974', 'http://www.vegasgrille.com', 'http://www.jubeelieve.com', 'http://www.jawman.com/', 'https://www.kneaded-tranquility.com', 'http://www.ilfornaio.com/lasvegas', 'http://www.macssushi.com', 'https://www.bostondentalgroup.com/locations/affordable-dental-sahara/?locations=Sahara', None, 'http://www.yumilarosa.com', 'http://www.magicoven.com', 'http://www.interiorsewingbykim.com/', 'https://assistedlivinglocators.com/care-advisor/Phoenix?utm_source=Yelp&utm_medium=Organic&utm_campaign=Organic&utm_content=Yelp&utm_term=Yelp', '1592488008', None, 'https://100academy.org/m/', None, 'http://www.treehuggerscafe.com', 'http://tempbodytattoo.com', 'http://www.avalonexchange.com', 'https://www.ravenphx.com', 'https://popcorngirlvegas.com/locations/henderson-location', None, 'http://midwestbeautyhouse.com', 'https://www.chevronwithtechron.com', 'http://www.carolinacustomwheels.com/', 'https://sunsetstation.sclv.com/Dining/Feast-Buffet?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'https://agent.amfam.com/kurt-bojarski/az/goodyear/15655+w+roosevelt+st/', '1592488045', None, 'https://locations.wendys.com/united-states/oh/cleveland/13939-euclid-ave.', 'http://www.barknscratch.ca', 'http://mightymeeple.blogspot.com', 'http://www.eastvalleyloveallpets.com', None, 'https://alltribes.com', 'http://casinomontelago.com/dining', None, None, '1592488067', 'http://www.JimmyJohns.com', None, 'http://www.smashburger.com', 'http://canyonclublasvegas.com', 'https://www.wyndhamhotels.com/hotel/23012?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:23012', 'https://www.cfshops.com/chinook-centre.html', 'http://www.junkmagicianllc.com/', None, None, 'https://www.chezjordan.com', 'http://www.huhot.com', 'https://www.randallsartandframe.com', 'https://www.innovativenow.com', None, 'http://hardackerroofing.com', 'http://www.emerilsrestaurants.com/e2go', None, 'http://www.azexoticpets.com/', 'http://www.skyzone.com/Leetsdale', None, 'http://www.affinitykitchens.com', 'https://teamturflawns.com', '1592488121', 'http://www.intimatelv.com', None, 'http://www.hrrocksinonorthfieldpark.com', None, 'https://www.chilldesserts.com', 'http://www.rosariospizzeria.com', 'http://locations.in-n-out.com/80', 'http://Www.unionpieco.com', None, 'http://www.atenderdentalcareaz.com', 'http://www.westsidemarket.org/', None, None, 'http://www.goldensunrisekitchen.ca', 'https://www.shearexcellence.com/dilworth/', 'http://www.dunkindonuts.com', 'http://www.lvsupercleaners.com', 'https://www.strangelovecoffee.ca', '1592488162', 'https://eyemagination.shop', 'https://www.grayhawkawards.com', None, 'http://www.eatmorefellinis.com', 'https://www.mrtbistroviet.ca', 'https://www.bardoptical.com/eye-doctor-in-champaign/', 'https://arizona.weidner.com/apartments/az/phoenix/aspire-pinnacle-peak/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'https://www.aspensquare.com/apartments/nevada/las-vegas/vue-5325?utm_medium=Yelp&utm_source=Yelp', 'http://nevadadivorce.co', None, None, 'http://biagionails.wix.com/spas', None, 'http://www.willowpgh.com', None, 'http://www.baskinrobbins.com', 'http://www.laonda2.com', None, None, 'https://www.artemano.ca', 'http://ginosmadison.com', None, 'http://www.aznypdpizza.com', '1592488220', 'https://rockhill.adventureairsports.com', 'http://www.pamelasofmonroe.com', 'http://www.arizonabraces.com', 'https://bebsicareforkids.com', '1592488233', 'http://www.mySHLonline.com', 'http://www.urbanaplumbingandheatinginc.com', None, 'http://epiphanydermatology.com', 'http://locations.michaels.com/AB/CALGARY/3902/', None, 'http://www.motioncorp.com', None, None, 'http://www.yvesrocherusa.com/control/main', '1592488260', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.bobebe.com', None, 'https://www.riteaid.com/store-details?storeNumber=01570', 'http://www.imsphoenix.com', 'https://www.benjaminnadig.com', 'https://gadgetmates.com', None, None, 'http://www.sunrisemidwifery.com', 'http://sewickleyeyegroup.com', 'http://www.boilingpotnc.com', 'http://www.streetsofnewyork.com', 'http://www.sunshinelandscapinglv.com/', None, 'http://www.gspawn.com/', 'http://www.eastsidecannery.com/dining/the-deli', 'http://www.alliancedermatology.com', '1592488304', 'http://flopysautodetail.com', 'http://Penrodduilaw.com', None, 'http://www.plazavalleyfield.com/', 'http://advancedneckandbackcare.com/', 'http://phxmetro.mrelectric.com', 'http://www.starbucks.com/store/9298/', 'http://www.scottsdaledentist101.com/', None, 'http://www.brilhoservices.com', 'http://cuginositalian.com', 'https://fixauto.com/calgary-coachworks-south', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', 'http://unionstreetbistro.com/', 'http://www.serviceking.com/locations/service-king-champaign?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', None, '1592488346', 'http://www.lasvegasmetroawnings.com', 'http://www.cashamerica.com/SUPERPAWN-stores/NV/LASVEGAS/LV12', None, 'https://www.audioexpress.com/locations/1140-e-sahara-ave-las-vegas-nv-89104/', 'https://www.foothillssmilesdentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'https://www.cantamarapartments.com', 'http://www.excelfloorcare.com', 'http://locations.arbys.com/us/nv/north-las-vegas/1465-w-craig-rd.html', 'http://www.torontovanlines.com', 'http://www.amtrak.com/', None, None, 'http://www.gondellateam.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.ariatroofing.com/', 'http://www.toronto.ca/parks/prd/facilities/complex/70/index.htm', None, None, None, 'https://www.raisingcanes.com/location/now-open-kent', 'http://www.imtwc.com', None, 'http://www.greenvalleysecuritylv.com/', None, None, '1592488406', 'https://www.no1bobatea.us', None, None, 'https://perfectnailbar.business.site', '1592488417', 'https://www.thecoreinstitute.com', 'http://www.costcutters.com/', None, None, None, 'http://mcldaz.org/perry', 'http://www.paysmerveilles.com/fr', None, 'https://reservations.mgmmirage.com/bookingengine.aspx?host=hotel&pid=190&utm_campaign=yelp_cta&utm_medium=general&utm_source=bellagio_cta', 'http://www.booradleys.ca', '1592488445', 'http://www.robertlawnservice.com', 'http://www.elitesf.com', None, 'https://www.chiefbauer.com/?utm_source=Yelp&utm_medium=ppc&utm_campaign=PinDot', None, 'http://nevadarecycling.com', 'http://www.gpoa.com', 'http://www.originalroccosfamousphilly.com', 'https://www.media41.us', 'http://www.spacephx.com', 'http://www.revolutionego.com', 'https://www.servpronorthcentralmesa.com', 'http://www.wokfo-u.com', 'https://www.klinkecleaners.com/locations/dane-county-locations/monroe-street', 'https://www.meineke.com/locations/pa/pittsburgh-1109/?utm_source=yelp&utm_medium=xvc', '1592488484', 'http://www.xoxojamelle.com', None, 'http://www.miamifades.com', None, 'http://www.carlsjr.ca/index.php?option=com_webmapplus&view=location&id=18', 'http://www.thebodyshop-usa.com', 'http://www.chastainsauto.com', None, 'https://www.starbucks.com/store-locator/store/10979', None, 'http://www.cooptopticalfairlawnoh.com', 'http://www.cicis.com/locations/nc-charlotte-10707-park-rd', None, None, None, 'http://tremontathletic.com', 'http://www.danilarosesalon.com/', None, None, 'http://www.platosclosetcalgarysouth.com', 'http://habitatofportage.org/restore/', None, 'http://www.sobelspineandsports.com', 'http://www.verizonwireless.com/b2c/index.html', 'http://www.JimmyJohns.com', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2fnc%2fcharlotte%2funiversity-place&sisearchengine=1524&siproduct=2529_Bus', 'http://www.streatburger.com/', 'https://palmbeachtan.com/locations/NC/Charlotte-East-Woodlawn-Road?utm_source=Yelp&utm_medium=banner&utm_content=website&content=AUG', 'http://garzagaragedoorservice.com', None, 'https://locations.dennys.ca/AB/CALGARY/248179', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/14600+Lawyers+Road+Corner+Of+Stevens+Mill+Road-Matthews-NC-28104/storeid=2877?cid=ps_ylp_2020', None, 'http://www.sunshinecraftco.com', 'https://www.walmart.com/store/1598/phoenix-az/whats-new', 'http://www.originalchimneys.com', 'http://123nailsandspa.com', None, 'http://carolinacarpetcleaning.net', 'http://www.greatspacesforplaces.com', 'https://www.panerabread.com/en-us/home.html', 'http://www.neededmassage.com', 'http://www.azhouseofcigars.com/', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'https://www.gyubeejapanesegrill.com', None, 'http://nhtownshippediatrics.org/', 'http://www.drbrokloff.com', None, 'http://hornemazda.com', None, 'http://arrowheadexterminating.com/', 'http://www.nandos.ca/restaurants/oakville-coming-soon', 'http://www.lablancabridal.com', None, None, 'https://www.americafirst.com/about/branches/branch-details.cfm?siteNo=104', 'http://www.harkinstheatres.com', 'https://pitapit.ca/location/#/en/scarborough', None, 'http://www.automation.agency', None, 'https://order.subway.com/Default.aspx', None, 'https://elementsmassage.com/yelp-herbal-ritual-special?loc=Goodyear', None, None, 'http://www.china-palace-restaurant.com', 'http://www.she-flirts.com', 'http://www.thebarrecode.com/studio/pittsburgh-shadyside', 'http://www.adultsource.ca', 'https://www.walgreens.com/locator/walgreens-900+ralston+ave-belmont-ca-94002/id=63', 'http://www.techwyse.com', 'http://www.bostonpizza.com', 'http://www.hair-dosalon.com', None, 'https://www.wincofoods.com', 'http://www.blsindia-canada.com/index.php', 'http://barre3.com/studio-locations/southpointe', 'http://www.thealamo.com', None, 'http://www.nailswithlovelv.com', None, 'https://www.pteglv.com/locations/sean-patricks/southern-highlands-st-rose/', 'http://troffservices.com', 'http://www.dollartree.com', None, 'http://www.acesplace.ca', None, None, None, None, 'http://www.redthesteakhouse.com', 'http://www.penzeys.com', 'http://www.desertviewlearningcenter.com', 'http://remedysalonspa.com', 'https://cabinetstogo.com/monroeville-pa', 'https://www.metro.ca/en/find-a-grocery/317', '1592488715', '1592488718', '1592488721', 'https://www.simonmed.com/locations/all/simonmed_imaging___copperpoint', 'http://www.jilsonsconsignment.com/', 'https://www.soulcounselingnv.com', 'http://www.welcometohost.com', 'https://disabilityhelpgroup.org', 'http://thetaj.ca/', 'http://www.candyfavorites.com/', 'https://www.pizzaville.ca', None, 'http://recessclt.com', 'http://www.atriumdental.net/', 'http://fabulous-floorscleveland.com', 'http://www.stitchylizard.com', 'http://www.tacobell.com/', 'http://www.transwarehouselv.com', 'https://wrench.com/las-vegas-nv-mobile-mechanic/?utm_campaign=lasvegas&utm_medium=organic&utm_source=yelp', 'https://locations.davidstea.com/on-richmond-hill-199', 'http://www.volaris.mx', 'http://www.sushi-koko.com', None, None, 'https://star-power.com', None, 'http://www.thedavenportsalon.com/', 'http://www.centeratarrowhead.com', 'https://curaleaf.com/stores/pl/curaleaf-gilbert-85233/', 'http://www.sallybeauty.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.vegasmotorcars.com', 'https://www.hushcanada.com/hush-calgary-north-west', 'http://www.forbicisalon.net', 'http://www.maximumoffroad.com', 'http://www.sprinklerworld.com', 'http://www.comprehensivewomenshealthcare.net', 'http://www.carecottageaz.com', None, None, 'http://www.surprisearizonacarpetcleaning.com', 'http://www.castlecookemortgage.com', 'http://www.onthegoaz.com', None, 'http://www.seniorsummerschool.com/', 'http://www.sparklesbeautybars.com', 'http://www.GivingTreeRealty.com', 'http://www.nabilselectronics.com', 'http://devotedstrength.com', 'http://gartmantechnical.com/', None, '1592488894', 'http://www.childtime.com/your-local-school/huntersville-nc-2009/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://www.autoactionaz.com/', 'http://www.portofsubs.com', 'http://www.gvpm.com', None, None, 'http://fitness4home.com/', None, 'http://locations.smartandfinal.com/nv/las-vegas/728/', None, 'https://www.azride.com', None, 'http://www.tuckersmarketplace.ca', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.tireworks.net/locations/6455-south-pecos-road-las-vegas/', 'https://www.popeyes.com', 'https://www.citycenterlasvegasliving.com', 'https://www.radissonhotels.com/en/radisson/hotels/toronto-on-east', None, 'http://nailbarlv.com/', 'http://www.trane.com/residential/en/buying-a-trane/find-a-dealer.html/402034', 'http://www.houndandkitty.com', 'http://www.besttimerv.com', 'http://www.jacksongreyjewelers.com', '1592488991', 'https://bellabridesmaids.com/pages/bella-bridesmaids-las-vegas', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://theexperiencedmovers.ca', 'http://www.grapebistro.com', None, 'http://www.mindfulmystic.com', 'http://www.greatclips.com/', 'http://www.sascupcakes.com/', 'https://www.beautybrands.com/store-locator/ahwatukee.do', 'https://www.goaptive.com/phoenix?cid=ye', None, None, 'http://www.johnsonfitness.com', 'https://ohiopawnshops.net', 'http://martialartsmesa.com/', 'http://goatyoga.com', 'https://www.lapalomapetcremation.com', 'http://www.mllenail.com', None, None, 'http://www.officedepot.com', 'http://www.financeofamerica.com/locations/branch-profile?id=015b26bb-71f8-6483-85d2-ff00007a9d7f&zip=89113', 'http://www.ThePinkTutuBallet.com', 'http://www.superior-tire.com', 'http://www.lastdrop.ca', 'http://www.aperfecthue.com', 'http://www.precisiontune.com/CharlotteNC_NorthTryonSt', 'https://www.aspendental.com/dentist/az/phoenix/2827-w-peoria-ave-ste-101?utm_source=yelp&utm_medium=lociqyext&utm_campaign=Phoenix%2CAZ%28Metrocenter%29%7C%7CPhxMtro_AZ%7C%7C9387&utm_content=listing', None, 'http://www.ntb.com/store/7331/concord-nc-28027-5924?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'http://www.acostaplasteringinc.com/', 'https://www.kfc.ca/store/17295-leslie-street-newmarket', 'http://www.shippendodontics.com', None, None, 'http://asyouwishpainting.com', None, None, None, 'http://www.cineplex.com/Theatre/cineplex-odeon-crowfoot-crossing-cinemas', 'http://www.cicis.com/locations/nc-kannapolis-1000-cloverleaf-plz', None, 'http://www.stsharbellasvegas.org/', 'http://www.nailtrixcharlotte.com', 'http://www.azautotrends.com', 'http://www.acesgrille.com/', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'https://www.katespade.com/stores/en/kate-spade-chinook-centre', None, '1592489170', 'http://www.eastyorkcurling.ca', 'http://www.vocellipizza.com', 'http://www.midas.com/toronto/store.aspx?shopnum=9040&dmanum=857001', 'http://www.funhousecleveland.com', None, None, None, 'https://www.reddevelopment.com/collier-center/', 'https://www.greatamericanhandyman.com/contact/', 'http://ocarbon.com', 'http://www.bulldogtoronto.com', None, 'http://studiogsalonanddayspa.com', 'http://www.ginospizza.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.delishboutique.ca', None, 'http://www.macayo.com/location/east-charleston-las-vegas/', 'http://kendallandco.ca/fyi/retail/', None, None, 'http://www.drainworks.com', 'http://www.t-mobile.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.annaslinens.com/?utm_source=Yelp&utm_medium=Annas_Homepage&utm_campaign=Yelp', '1592489263', None, None, 'http://pizzaandbeyond.blogspot.in', None, None, None, 'http://www.eviltwincustomcycle.com/', 'https://www.budgetdumpster.com/westlake-oh-dumpster-rental-ohio.php', 'https://www.anytimefitness.com/gyms/2324/Rock-Hill-SC-29732/?utm_source=yelp&utm_medium=local', 'http://www.humbertosmexfood.com', None, 'http://miniso.ca', 'https://www.southstburger.com/location/130th-ave/', 'http://www.arizonaautoparts.com', 'http://www.uswigslv.com', 'http://www.wow1day.com/locations/house-painting-calgary', 'http://locations.saksoff5th.com/en/charlotte', None, 'https://www.discounttire.com/store/az/mesa/s/1294?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.alphadentistry.com', None, None, 'http://www.starbucks.com/store/9229/', 'http://www.bachiburger.com/', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', '1592489359', 'http://www.turquoisehousescottsdale.com', 'http://www.myfoodcity.com', 'http://rothcomputerregister.com/', None, 'http://fernhollowbicycles.com', None, None, None, 'http://www.toronto.ca/parks/parks_gardens/jamesgdns.htm', '1592489393', None, '1592489399', None, 'http://r-m-smoke-shop.business.site', 'http://www.azskinrehab.com', 'https://www.hallmark.com', 'http://www.veronapizza.ca/', 'http://www.stewartappliance.com', None, None, 'http://www.criscam.com', 'http://www.deluxrestaurant.ca', None, None, 'http://www.phoenixgaragefix.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.loredotireshop.com', 'http://dilworthtr.com', 'http://www.howardsjewelrycenter.com', 'http://www.kitsonandco.com', 'http://www.fcbanking.com', 'http://locations.arbys.com/us/pa/pittsburgh/4810-mcknight-rd.html', None, 'http://salonsanctuary.com', 'https://hpptraining.com', None, None, None, None, 'https://www.cosmopolitanlasvegas.com/restaurants/rose-rabbit-lie?utm_source=yelp&utm_medium=cpc&utm_campaign=yelp', 'http://orogoldlocations.com/portfolio/las-vegas', 'http://jmdesignbuild.com', 'http://www.aroma.ca/branches/', None, None, 'http://2ndchancevegas.com', 'https://reservations.mgmmirage.com/bookingengine.aspx?host=hotel&pid=930&utm_campaign=yelp_cta&utm_medium=general&utm_source=aria_cta', 'https://www.cinemark.com/north-carolina/cinemark-movie-bistro-charlotte?utm_campaign=int&utm_medium=organic&utm_source=yelp&utm_content=yelp_listing', '1592489515', 'http://absoluteplumbingnv.com', 'http://www.brendylelectric.com', None, None, None, None, None, None, 'http://www.organicedibles.org/', None, 'http://www.tigautomotive.com', 'https://www.hilton.com/en/hotels/phxpcht-home2-suites-phoenix-chandler/?SEO_id=YELP-HT-PHXPCHT', 'http://tiffanycafe.ca', None, 'https://www.hov.org', 'http://www.heinzlofts.com', 'https://locations.rallys.com/oh/cleveland/1481-west-117th-street/?utm_source=Yelp', None, 'https://www.steinhafels.com', 'https://www.healthysmoothiebartempe.com', None, 'https://www.regmovies.com/theatres/regal-boulder-station/0837?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Boulder+Station+&+VIP', None, 'http://www.sobeys.com/en/stores/sobeys-kipling/', None, 'http://www.hillcrestflorists.com', 'http://www.topgunfit.com/', 'http://www.santafestationlasvegas.com/', 'http://anoushrestaurant.com', None, 'http://www.mackaylaw.ca', 'http://arizonacrown.com/index.html', '1592489626', None, 'http://Www.comforthomepetservices.com', 'https://www.kitchen59.ca', 'http://www.bk.com', 'http://caseyinsulationinc.com', 'https://www.lovesac.com', 'http://www.incatea.com', 'https://hernandeztruckandauto.business.site', 'http://charlottenc.gov/AnimalsCMPD/Pages/default.aspx', 'http://www.boarnwing.com/#!formmap/c24vq', 'http://www.doorprosgaragedoors.com', 'http://www.tennysjamaicanfood.com', 'http://barisabel.com/', 'https://sparklyhousecleaning.com/free-quote/', None, 'http://www.ewtaz.com', 'https://stores.anntaylor.com/on/toronto/220-yonge-street.html', 'https://www.signaturestyle.com/locations/on/maple/first-choice-haircutters-51279.html', 'http://www.partyusacentral.com/', 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', 'http://www.encompasstheworldtravel.com', 'http://www.kenzoramen.com/', 'http://www.fyinktattoos.com', 'https://www.paletasicecream.com', 'http://downtowndonutsnc.com', 'https://jins-mi-fen.business.site', None, 'http://www.missmeatball.com/', None, 'https://www.palms.com/eat-and-drink/mr-coco/', None, 'https://www.autozone.com/locations/az/mesa/7659-e-guadalupe-rd.html', '1592489735', 'https://www.freewaychevrolet.com', 'http://www.arguementgolf.com', 'http://www.iceacake.com', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/calgary/yycmt/hoteldetail', 'https://locations.arbys.com/us/il/urbana/509-n-cunningham.html', None, 'http://www.abcairconditioning.com', '1592489759', 'http://www.tapsandtales.net/', None, 'http://www.specialmomentsaz.com', 'https://www.publicstorage.com/ohio/self-storage-bedford-heights-oh/44128-self-storage/1178?pid=wyelp&CID=1245&CHID=AFL', None, None, 'http://marcos.com/stores/south%20carolina/402-marcos-pizza-indian-land-south-carolina-29707', '1592489785', 'http://www.JimmyJohns.com', 'http://www.pitapit.com/', None, 'http://www.cpk.com/Location/Details/Summerlin', None, None, 'http://www.starbucks.com/store/9681/', None, None, 'http://www.scottsdaleazdentist.com/', None, None, '1592489824', 'http://www.nikkileessportsbar.com/', 'http://shamrockheatingandcooling.com/', None, 'https://passion-hookah-lounge-restaurant.business.site', 'http://www.gowiseproducts.com', 'http://www.rodgunandbarbers.com', 'http://local.firestonecompleteautocare.com/south-carolina/fort-mill/2326-parchment-blvd/?lw_cmp=IYP_YPC_MLP_343717', '1592489847', 'http://www.hillarylacy.com', 'http://www.NY54pizza.com', None, 'http://www.mccalls.ca/', 'http://www.usps.com', '1592489868', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.downtownsewingmachine.com', 'http://www.petco.com', 'http://www.rentcheckcorp.com', None, None, None, 'http://www.headlinesbarbershop.com', None, None, 'http://www.monicals.com/locations/monicals-pizza-of-champaign-w-kirby-ave/', None, None, 'http://www.caslv.org', 'http://www.thepilot.ca/', None, 'http://www.looseleafteamarket.com', 'http://chandlerpostacute.com', 'http://scottdentistryaz.com', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280191177&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.thegourmetburgerco.com/html/location/parliament.html', 'http://www.costumeworld.com', 'http://www.weldondentalcare.com', 'https://www.novanthealthimaging.com/locations/charlotte/south/novant-health-imaging-ballantyne/', 'http://www.pullnsave.com', None, 'http://www.davidthompsonbuilds.com', 'http://trusighteyes.com', 'http://winestore-online.com/', None, None, 'http://www.rutabaga.com', 'https://www.get-go.com/', '1592489991', 'http://www.campbowwow.com/us/nc/charlottemetro/', 'http://www.portofsubs.com/', 'http://www.opportunityvillage.org/', None, 'http://www.securityselfstorageltd.com/self_storage/highland_heights/zip_44143/security_self_storage/583', 'http://www.benairsystems.com', 'http://local.buckle.com/az/chandler/297/?utm_source=buckle&utm_medium=website&utm_campaign=store+locator', 'http://www.freehousedance.com', None, 'http://www.bridgetowntaphouse.com', None, 'http://www.laroccacafe.com', None, 'http://affordablelawnandsnow.ca/', 'http://www.biglots.com', 'http://johnandsonsoysterhouse.com', None, 'http://www.desertsportsfootandankle.com', None, None, 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', 'http://www.patcatans.com/craft-store-locations/strongsville-oh', None, None, 'http://www.jakayssalon.com', 'https://local44.ca', 'http://phoenixusedrestaurantsupply.com/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.tractorsupply.com', 'http://www.atlas-machinery.com', None, 'http://us.campero.com', 'http://www.karahiboys.com', None, 'http://www.phxbbq.net', 'https://www.macaronigrill.com/locations/location?id=1680', None, 'http://www.radiatorinfo.com/cgi-sys/defaultwebpage.cgi', 'http://charlestonchiropracticlv.com', None, None, 'http://www.fastlinetuning.com', 'http://www.zgallerie.com', 'https://www.geico.com/insurance-agents/north-carolina/charlotte/megan-donoho/', 'https://www.nvisioncenters.com/locations/las-vegas/alta-rose-eye-center/?utm_source=directory&utm_medium=yelp', None, 'http://pizzapizza.ca', 'http://www.artifactlv.com', 'http://www.winewalklv.com/', 'http://www.eastsidemarios.com/', 'http://www.visionholidays.com', 'http://www.catcafemad.com', 'http://www.lovemesweet.ca', 'http://www.alphamalenailcare.com', None, 'http://www.thaiplacepgh.com/', None, None, 'http://phoenix.cabinetcures.com/contact/', 'http://www.classiqueautospa.ca', 'http://www.spiffyauto.com', 'http://www.kathmanduartifacts.com', 'http://www.thepotatobarn.com', None, 'http://iboutique.net', None, '1592490229', 'https://kavasutra.com/pages/kavasutra-phoenix', None, 'http://metropolitan.coffee', 'http://www.screenmobile.com/Las-Vegas-West', 'http://www.bathandbodyworks.com', 'http://www.theguitarshop.ca', 'http://www.azrodentremoval.com', 'http://sonioscafelasvegas.taverndesigner.site', 'http://jamesstudio.com', 'http://www.regalnails.com/', 'http://www.papajohns.com/', 'http://www.thegreatsteak.com/stores/7424', None, 'https://www.pizza73.com', 'http://www.vicsfloral.com', None, 'https://www.choicehotels.com/north-carolina/charlotte/rodeway-inn-hotels/nc168/rates', None, 'https://www.suncityanimalhospital.com/?utm_source=yelp&utm_medium=social', 'http://www.eaglecrest-apts.com', 'http://www.canadiantire.ca/en/store-details/on/toronto-main-danforth-on.store.html', 'http://www.andysautobridgeville.com/', 'http://pvnailslounge.com', 'http://fideliselite.com', 'http://brilliantnailsspa.com', 'http://greek-palace.buisness.site', None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://zenspanail.com', 'https://salesfirstrecruiting.com', 'https://model-home-furniture-llc.business.site', 'http://www.villasatsunrisemountainapts.com', None, 'http://peak-autosales.com', None, '1592490347', 'https://www.azfd.com', None, 'http://www.smoothieking.com', 'http://www.yourescentialmassage.com/', 'https://studiovivian.com', None, 'http://www.sierraranchapts.com', 'http://www.crocketthoney.com', 'http://www.armedpersonaldefense.com', 'https://autohouse.com', 'https://www.bvoluxurygroup.com', '1592490390', 'https://elementsmassage.com/chandler-south', None, 'http://citgo.mycstore.com/15892051', None, None, 'https://www.purolator.com', 'http://www.mundotrattoria.com/', 'http://thirstyturtle.ca/', 'http://www.inthesky.com', 'http://www.omahasteaks.com/stores', None, 'https://maps.rbcroyalbank.com/locator/searchResults.php?t=2169', 'http://www.quiznos.ca', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'https://www.241pizza.com', None, None, 'http://rivertownantiques.com', 'http://www.delta.beer', 'http://www.hottiesworld.com', None, 'http://www.singertax.com', 'http://www.bamboochina.net', 'http://paradisebakery.com', 'http://leventhaldefense.com', 'http://pheasant.firkinpubs.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.orangetheory.com/en-us/locations/arizona/phoenix/7000-e-mayo-blvd-building-1-ste-1016/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, 'http://www.starbucks.com', None, 'http://pctravel.ca', 'http://tinunothirtyone.com', 'http://www.a2zautoexclusive.com/', 'http://www.altardstate.com', 'http://www.dungymd.com', 'https://www.cash1loans.com/Locations/NEVADA/Las-Vegas-Cheyenne.aspx', 'http://www.absolutepestsolutionsaz.com', 'http://vipizzacramerton.com', 'https://www.iqfoodco.com', 'https://www.pokespotaz.com', 'http://www.lvtailor.com', 'http://locations.saksoff5th.com/en/vaughan-mills', 'http://www.dinerdeluxe.com', 'http://www.nice1nails.com', None, 'http://www.alterahighland.com/', 'http://doughremidonuts.com', None, None, 'http://www.drjlittlesmiles.com', 'http://www.timhortons.com/', None, None, 'http://www.cicispizza.com', 'http://www.mimispettransport.com/', 'http://www.vegasvacuumsewing.com', None, None, 'http://www.eclipsesunscreens.com', 'http://vegas.renttext.com/', 'http://www.srtmedstaff.com', 'https://www.bachelorettevegas.com', None, 'http://www.charlottencacupuncture.com', 'http://www.compassbank.com', 'http://www.sushidate.ca/', 'http://yo-i.happytables.com/', 'http://www.danaraiabridal.com', 'https://www.autoglassshopchandleraz.com', 'http://www.nexuselectricservice.com', None, 'http://www.apdpowercenter.com', None, 'https://www.micelifamilychiropractic.com', None, '1592490629', 'http://www.gastonautoglassinc.com', None, None, 'http://www.TopGreenCleaning.com', None, 'http://alphillipslv.com/', None, 'http://cookiegrams.com/', 'http://www.consiglioskitchenware.com/store/pc/location.asp', 'http://www.oakvilletemplebarpub.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', None, 'http://www.perogyboyz.com/', None, 'https://www.carlow.edu', None, None, 'http://www.swcwc.net', None, 'https://sunrisehospital.com/service/the-breast-center-at-sunrise', 'http://brimhalleyecenter.com', '1592490694', 'https://beonair.com/locations/cleveland', 'http://www.escaparium.ca/laval', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.tuina.ca', None, 'http://chirofitgroup.com/', None, 'http://www.prettypleasefashion.com', 'https://www.chamsine.org', 'http://www.bathandbodyworks.com', 'http://www.dunkindonuts.com', 'http://rusticridgekennels.weebly.com', 'http://www.luxehairaz.com', None, 'http://www.mideastroyorkville.com', 'http://royalblush.ca', 'http://www.starbucks.com', None, 'http://poppyseedsbagels.com', 'https://www.quartierdix30.com', 'https://www.7threstaurantandlounge.com', None, 'http://www.canyonkitchencabinets.com', 'http://fletcherlv.com', 'http://www.marcos.com/', 'http://tangledrootbotanicals.com', None, None, None, 'http://www.no5hairco.com', 'http://aurafitness.ca', 'http://anbnf.com', None, 'http://visionsource-eyesiteofanthem.com', 'http://www.bellagio.com/spasalon/spa.aspx', None, None, 'http://www.allmetrodriving.com', 'http://carolinajerky.com', None, 'http://www.debakerdental.com/', 'http://www.southcharlottebanquetcenter.com', None, 'http://www.trairporttransportation.com', 'http://www.cublindman.com', None, None, 'http://www.alibabas.ca', None, 'https://www.chamberedusa.com', 'http://www.rubbishworks.com/phoenix', '1592490859', 'http://www.therunnersshop.com/', 'http://mihs.org/', 'http://www.rolledicecream.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sagicor.com', '1592490884', 'http://derkasautobody.com', 'http://www.BugmanAZ.com', 'https://www.walmart.com/store/1532/glendale-az/whats-new', 'http://www.thegritty.com/sun-prairie', None, 'http://www.perryellis.com?utm_source=Yelp&utm_medium=Social&utm_campaign=PE_Yelp_BioCTA', 'https://arizonatacos.com', 'http://www.naturalwellnesscentre.info', 'http://www.sevenviewchrysler.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.staples.com', None, '1592490933', 'http://www.litehouse.com', 'http://sassi.ca', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', 'http://studio23-hairdesign.com', None, 'http://www.8thandhays.com', None, 'https://ikonicdanceconnection.com', 'http://edmarshalljewelers.com', 'https://godsgarden.com', 'http://lasvegas.jiffylube.com/Locations/Store/1975/4531-N-RANCHO-RD-LAS-VEGAS-NV-89130-3403', 'http://www.fasslauto.com', 'https://locations.nekterjuicebar.com/ll/US/AZ/Tempe/2000-E_-Rio-Salado-Pkwy_*-Ste_-1213?utm_source=yelp&utm_medium=link&utm_campaign=Tempe&utm_content=URL', 'http://appliancerepairconcord.nc-biz.co/', 'http://www.rayssplashplanet.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.fireflylv.com', None, 'http://www.amecuisine.com', 'http://royalvegastours.com/ipartyinvegas-concierge-service', 'http://newwaterplumbing.ca', None, 'https://www.amctheatres.com/WinstonChurchill', None, 'http://b2lchiro.com/', 'http://www.brightnow.com/locations/dental-office/Phoenix/Bright+Now+Dental/40020', 'http://lightitupaz.wix.com/smokeandvapeshop', 'http://www.warraichmeats.com', 'http://platinumphotographyohio.com', None, 'http://locations.avis.com/us/al/madison/m6o.html', 'https://cupcakeschampaign.com', 'http://supersummertheatre.org', '1592491044', 'http://www.residentialassistedlivingacademy.com', None, '1592491051', None, 'http://www.unionpgh.com/', None, 'http://www.villagelanesmonona.com', 'https://sun-energy-smoothies.business.site', None, None, 'https://www.arizonaurologyspecialists.com/contact-phoenix-osborn', 'http://www.platinum.ca', 'https://locations.rallys.com/oh/cleveland/1481-west-117th-street/?utm_source=Yelp', 'https://www.kohls.com/stores/az/avondale-660.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.antaplumbing.com', 'http://centerstagenoda.com', None, None, 'http://slicedgourmet.com', 'https://onenorman.com', 'https://www.chick-fil-a.com/belmont', None, 'http://www.sassconsignment.com', 'http://www.josephscottsalon.com', 'http://www.dizylounge.com', 'http://www.LifeCenterPlus.com', None, 'https://scapetechlandscapes.com', None, 'http://www.hardees.com', 'http://www.bridalwearhouseusa.com/', None, None, 'https://zebra-nails-spa.business.site', 'http://www.cupidscupcakes.ca/', 'http://Avondalefamilydentalcare.com', 'http://thenewparadiselounge.com/', 'http://www.dukesribhouseandgrille.com', 'https://smiledirectclub.ca/en-ca/smileshops/toronto-markham/?utm_campaign=yelppaid&utm_medium=cpc&utm_source=yelp&utm_content=torontomarkham', 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', 'http://www.shopnofrills.ca', 'http://www.livingartsalon.com', 'http://lasfuentesmexicangrill.com/', 'http://www.suherdental.com/', None, None, 'http://www.kirksstudio.com', 'https://www.HealthBrokersOnline.com', 'http://rawlicious.ca/canada/locations/newmarket/', 'https://www.familydollar.com/locations/az/phoenix/26308', 'http://www.timhortons.com/ca/locator/storedirections.html?id=100913', 'https://www.airdrieglass.com', 'http://www.mrwonderfuls.com/', None, 'http://www.scoopspittsburgh.com', 'http://www.bodynbrain.com/montecito', 'http://vinylrecorddude.com', None, None, 'https://www.sprint.com/storefronts/bd/sprint-las-vegas-nv-89119-fcs-748/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.coach.com/', 'https://www.famousfootwear.com/?partnerid=YELP', None, None, 'http://onthearm.lv/shop', 'https://www.long-mcquade.com/location/Alberta/Calgary/', None, None, 'https://theyoungteam.com', 'http://www.kingswaydermatology.com', 'http://www.lolitaslounge.ca', None, 'https://www.revitalizesewickley.com', 'http://silktoronto.ca', 'http://steak44.com', None, 'http://www.mazdaofrichmondhill.com', None, 'http://fresh.longos.com', 'http://www.eyedistrictbyjo.com', 'http://www.beyondmassagetherapy.com/', 'http://www.urbayn.com', None, 'http://www.woofwagonaz.com', 'https://lipo.sonobello.com/yelp/?inetcampid=1447', 'http://www.greatclips.com/salons/3065', 'https://www.rockledgefairways.com', 'https://locations.theupsstore.com/nc/charlotte/2820-selwyn-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://acrobatcaddies.golf', 'http://www.synergycharlotte.com', 'http://www.sweetjesus4life.com/', 'https://www.target.com/sl/charlotte-midtown/2244', 'http://www.theemmetray.com/', 'http://www.tycobuilt.com', 'http://www.jackrabbitaz.com', None, None, 'http://www.arns.ca', 'http://www.hottopic.com', 'http://www.thorncrest.com/', None, 'http://www.michelleshairboutique.com', None, 'http://colleendds.com', 'http://www.autonationtoyotalasvegas.com', 'http://www.stonemillbakehouse.com', 'http://uskdental.ca/', 'http://www.mindfulmassagephx.com', '1592499470', 'http://www.venetian.com/Pages.aspx?id=362', 'http://glwb.net/', None, None, None, 'http://hardhatbar.com/', 'http://www.clarksusa.com', 'http://www.tantasia.ca', 'http://hellobistro.com', None, 'http://www.naturecure4you.com', None, 'http://us.suitsupply.com/en_US/store?StoreID=stores-Phoenix&utm_medium=referral&utm_source=yelp&utm_campaign=Scottsdale', None, '1592499511', None, None, 'http://www.bar-italia.ca', 'http://www.idealfoods.com', 'http://www.kellyskawasaki.com', 'http://locations.michaels.com/az/glendale/2763/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.newdriversofalberta.net', 'https://www.capriottis.com', 'http://tabletopsetc.net', '1592499539', None, 'http://www.prmaz.com', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'http://www.winghouseandsportsbar.com/', None, 'http://www.muffcakesbakery.com', 'http://jmiconcrete.com/res_contact.html', None, 'https://vntghome.com', 'http://www.purecreations.ca', 'http://harlowvegas.com', None, 'http://www.menchies.com/frozen-yogurt-shops/frozen-yogurt--northland-plaza-ab', 'https://www.certifiednannies.com', 'https://bentcrayonrecords.com', 'http://www.midas.com/pittsburgh/store.aspx?shopnum=6394&dmanum=688', 'http://americanappliancecompany.com', 'http://www.greasewoodflat.net', 'http://www.sweetblissleslieville.com/#about', 'http://www.moonbeancoffee.com', '1592499594', 'http://www.samuraisams.net', 'http://www.glendaleca.gov', 'https://www.nsbank.com/branch/?branch=durango_and_215_south_branch', 'http://www.coleylawfirm.com', 'http://JohnBaileyLV.com', None, 'http://www.agentheather.com', '1592499614', None, 'http://www.dinospizzapasta.com', None, 'http://www.propertymgt.com/', 'http://trektoronto.ca', '1592499630', 'http://www.mwtvproductions.com', 'http://clevelandyoga.com', 'https://www.pizzahut.ca/#!/home', 'http://www.flogatoronto.com', None, 'https://www.carprosparma.com', 'http://www.randolphlawfirm.com/', None, 'https://www.hotelartskensington.com', 'http://enterprisetreeservices.com', 'http://dreamdinners.com/main.php?page=store&id=193', None, None, 'http://www.pediatricdentalcareassociates.com', 'https://www.baylesshealthcare.com/locations/bella-vista/', None, None, 'http://yahsbest.com', 'http://emberslasvegas.com', None, None, None, 'http://www.muchoburrito.com', 'http://www.celebrityphotoboothlv.com', None, None, None, None, 'http://www.partycity.com', 'http://georgec.ca', 'http://www.frommsmithandgadow.com', 'http://www.starbucks.com/store/9229/', 'http://www.21mike.com', None, None, None, None, 'http://www.thesportinggent.com/', 'http://www.china8.ca', 'http://locations.qdoba.com/2303/?utm_source=Yelp_Listings', 'https://www.pestcontrolinc.net', '1592499734', 'http://croffootheating.com', 'https://mclifephoenix.com/property/the-place-at-sonoran-trails/', 'http://www.thompsonpoolservice.com', None, 'http://dundaswestfest.ca/', 'http://www.jlpatisserie.com', None, 'http://www.azcustompools.com', 'http://torontohypnotherapy.ca', 'http://www.acehelpful.com', None, 'https://cortland.com/apartments/attiva-court/', None, None, 'https://www.tripleamotorsports.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.designspacepgh.com', None, 'https://locations.theupsstore.com/oh/akron/3465-s-arlington-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.canopyatbaybrookapts.com/?utm_source=Yelp&utm_medium=LPCSEO', 'http://wagspgh.com', 'http://www.rossstores.com', 'http://www.stevansconsignment.com', 'http://cavaliermgmt.com/The_Edge.aspx', 'http://www.palms.com/see-and-do/wellness/pool-at-palms-place?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'https://www.smdisasterrecon.com', None, 'http://www.inspiradaanimalhospital.com', 'http://greenvalleygaragedoorsllc.com', 'http://www.brsvegas.com', 'http://acuraofnorthtoronto.ca/', None, 'http://www.bestwokphoenix.com', '1592499828', 'http://www.heymeatball.com/', 'https://www.chick-fil-a.com/rossparkmall', '1592499835', '1592499838', 'http://www.homesealed.ca', None, 'http://www.ymcacharlotte.org', 'http://www.teamvegasbasketball.com', '1592499852', 'http://www.xpresstaxaz.yolasite.com', None, None, 'https://www.amazingnailsandlash.com', None, 'https://steelcitymeats.com', 'http://www.chagrinanimalclinic.com', 'http://www.clearbritepools.com', None, 'http://muncheespopcorn.com', 'http://jbamotors.com', None, None, '1592499885', 'http://www.tkmtacademy.com', None, 'http://www.jeetcafe.net', 'http://hudsongoodyear.com/tires-auto-repair-hudson-oh', 'https://www.anytimefitness.com/gyms/2441/Brampton-ON-L6P-2R1/?utm_source=yelp&utm_medium=local', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, '1592499905', 'http://eatPDQ.com', 'https://www.target.com/sl/amherst/2351', 'http://www.altolounge.com', 'http://www.vegas-comics.com', 'http://mojaveandscaping.com', None, 'https://mule-creek-saloon.business.site/?utm_medium=referral&utm_source=gmb', None, None, 'https://fixautousa.com/glendale', None, '1592499936', 'http://www.johnallensaz.com', 'http://www.dolce-salon.ca/dolce/about.html', None, None, None, None, 'http://www.wintercpas.com', None, None, None, None, 'https://www.choicehotels.com/CN327?mc=blypypaf', 'https://j-js-family-restaurant-catering.business.site', '1592499966', None, None, 'http://www.commonbondyyc.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, 'http://www.unitsinjectionspa.com', None, 'http://www.arizonaairandheat.com', '1592499994', 'http://a3napoli.com/', 'http://www.ippai.ca', 'http://www.shieldsfamilydentistry.com', None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.suzygoodrick.com/', 'http://hulshoffarmmarket.com', 'http://disasterrescue.com', 'http://www.chengdutastevegas.com', None, 'http://www.copperrents.com', 'http://www.kinglyclean.com', None, 'http://www.rmpconstruction.com/', 'http://www.bringemyoungacademy.com/', None, 'http://www.glovskyortho.com/', None, 'http://www.frysfood.com', '1592500056', 'http://www.cottonon.com', None, None, None, None, 'http://www.weatherguardrestoration.com', 'http://www.VCardLasVegas.com', None, 'http://tremonttaphouse.com', None, 'http://www.steve-tarrant.com?cmpid=NQWF_BLM_0006', 'http://www.LemonStreetTacos.com', 'https://www.olivegarden.com/locations/nv/las-vegas/las-vegas-cheyenne-ave/1363?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:las-vegas-nv-1363_pl:locurl_rd:1274', 'http://www.azmediquip.com', 'http://www.dine.to/sites/wheatsheaftavern/', 'https://www.FurnitureRow.com/shared/location/FurnitureStoresInCharlotteNCFurnitureRow/100065?utm_source=FurnitureRowYP&utm_medium=display&utm_campaign=YP', None, 'https://www.avillahomes.com/homes/avilla-town-square', None, None, None, 'http://www.cleantheory.co', 'http://www.skc.agency', 'http://www.hibachisan.com', 'http://www.apizzabadamo.com', 'http://www.oldchicago.com/', '1592500122', 'https://www.jewelryexchange.com/phoenix-arizona-diamonds-jewelry-store-jewelryrepair', 'http://www.dunhamssports.com/stores/sporting-goods-pittsburgh-pa/', 'http://www.delanohairsalon.com', None, 'http://www.infinitysend.com', 'https://www.hideawaylakeapartments.com/?utm_source=Yelp', '1592500140', 'https://positivelypolaraz.com', 'http://www.amethystcolony.com', '1592500147', 'http://ahipoki.com', 'http://www.starbucks.com/store/9229/', 'https://www.pnc.com/en/personal-banking.html', None, 'http://www.richardswindowtinting.com', None, 'http://www.hurrycurry.ca/index.php', 'http://www.snapfitness.com', '1592500170', None, None, None, 'http://info.tradesecrets.ca/locations-reviews/yonge-st-clair/', 'http://www.officedepot.com/storelocator/az/tempe/officemax-6276', None, None, 'http://www.dairyqueen.com/us-en/store-details/12001/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://artisticiron.com/powder-coat', 'https://www.threeriversroofing.net', None, None, 'http://www.gregorytglass.com/arizona-winter-2020', 'https://nothingbundtcakes.com/bakery/AZ/gilbert?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=gilbert_216', None, '1592500212', 'http://www.pokewave.com', 'https://www.lookstylesociety.com/gentlemens-quarters/', None, 'http://www.cbac.com/huntersville?utm_source=Social&utm_medium=Yelp', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.timelesstattoolv.com', 'http://www.anyplaceautorepair.com', None, 'https://clt.2ulaundry.com/clean/yelper/?utm_campaign=clt+%2F+signups+%2F+all&utm_medium=paid+social&utm_source=yelp', None, 'http://www.marriott.com/hotels/travel/cakfl-residence-inn-akron-fairlawn/', None, None, 'http://www.scottthomas.biz?cmpid=PODJ_BLM_0006', 'http://www.albertahealthservices.ca/facilities.asp?pid=facility&rid=2', 'http://www.5anddiner.com', 'http://www.unlvrebels.com/trads/unlv-trads-wilson.html', 'http://www.stationsquare.com', 'http://www.thegrover.com/', 'https://stores.shoecarnival.com/oh/medina/shoe-store-medina-oh-254.html', 'http://www.newkensingtonfloral.org/?srccode=yelp_track', None, 'http://www.turtlecreeknursery.com', None, 'http://www.kronenrealty.com', 'http://timscornerbar.com', 'https://www.heritagepoolplasteringnv.com', None, None, 'http://www.alsrv.com/', '1592500326', 'http://www.danceshoppe.com', None, 'http://sportclipsmajormackenzie.ca', 'http://addisonlandscapes.com/', 'http://www.ClevelandCycleTours.com', 'http://www.andreasmenshaircuts.com', 'http://www.midas.com/toronto/store.aspx?shopnum=9105&dmanum=857001', None, None, 'http://wekopa.com/clubhouse/we-ko-pa-grille/', '1592500365', '1592500371', 'http://assemblepgh.org/', 'https://www.batteriesplus.com/store-locator/az/mesa/batteries-plus-334?utm_source=yelp&utm_medium=local&storecode=334', '1592500379', 'http://www.homehardware.ca/en/dealer-microsites/1801-1/contact-information.htm', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', 'http://www.nobledesigns.co', 'http://localerestaurants.ca', None, 'http://www.nextlevelgymnastics.net/', 'https://stores.pepboys.com/az/mesa/7715-e-main-st.html', 'https://paulbeaunenysalon.com', None, 'https://biryanicorner.ca', None, None, 'http://www.petersoncompany.com', 'http://www.bi-lo.com', 'http://www.nafnafgrill.com', 'http://www.marcos.com', None, 'http://solarestire.com', None, 'http://www.mypureform.com', 'http://www.akropolispastries.com', 'http://hotovenbakery.com', 'http://www.tuesdaymorning.com/index.jsp', None, 'http://lifecarecenterofscottsdale.com/', 'https://www.cyclegear.com', None, 'http://a2zestatesalesaz.com/', None, 'http://www.shoplostfound.com/', None, 'http://somersetskypointe.org/', None, 'https://wavescoffee.com/our-stores/springborough', 'http://www.mesaconventioncenter.com', 'http://habitatcaz.org/restore', 'http://www.shalimarweddingchapel.com/', None, None, 'http://pulpjuiceandsmoothie.com', None, 'http://www.alumnaetheatre.com', 'http://drwilliamfrancis.com/', 'http://www.bouldercityflorist.com', None, 'http://www.thetraditionapts.com', 'https://www.valvistagardensapts.com', 'http://www.einsteinbros.com', None, 'http://starcrestcleaners.net', 'http://www.paologattuso.com', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', '1592500561', 'https://www.choicehotels.com/ohio/warrensville-heights/econo-lodge-hotels/oh474?pmf=yelp&mc=blypypaf', 'http://sic2012.wix.com/southindiacuisine', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://floydsveteranconcrete.com', 'http://www.centurylink.com', None, None, '1592500597', 'http://eliteartandframing.com', 'http://www.kasturicanada.com', None, 'http://www.footcarecliniclv.net/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://plentyofplaces.com/nevada-properties/park-avenue/', 'http://markhamhonda.com/', '1592500630', 'http://rossogelato.com', 'http://www.automotiveimportmarket.com', 'https://www.napaonline.com', None, 'http://www.georgyporgys.ca', 'http://www.solcaribeaz.com', 'https://www.cadence-academy.com/schools/huntersville-nc-eastfield-preschool/?utm_source=yelp&utm_medium=local_listing&utm_campaign=yelp_website&cad_campaign=yelp_website', '1592500657', 'http://www.gmstactical.com', 'http://www.mrosmow.com', 'https://stores.pandora.net/en-ca/on/scarborough/pandora-jewellery-ca4215763e.html', None, 'http://www.stefanecsdeluxebarbershop.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', None, '1592500688', 'http://info.tradesecrets.ca/locations-reviews/yonge-st-clair/', 'http://www.antoniaadamsphotography.com', '1592500700', 'http://www.ultracleanexpress.com', 'http://www.treasuredcutz.com', 'https://www.azdentistry.com', None, 'http://www.mauriesfinechocolates.com', 'http://www.Yahwehyoga.com', None, 'http://www.glowskinbodystudio.com/', None, None, None, None, None, 'http://healthyhabithealthfoods.com', 'http://bethyeshualv.org', None, 'https://www.ifixitusa.com', 'http://www.bungalow.to', None, 'http://www.ilovekickboxing.com/kickboxing-studio/index.php?id=443', None, 'https://www.dvusd.org', 'http://www.vixenspa.com', 'http://www.danawater.com', 'https://www.miniofpittsburgh.com', 'http://www.houseofblues.com/lasvegas/crossroads', 'http://belmontvillage.com/scottsdale', None, '1592500808', 'http://www.pawnplaza.com/', 'http://signofthewhaleaz.com', None, 'http://www.Unos.com/?utm_campaign=YelpTest&utm_medium=ctr&utm_source=yelp', None, 'http://theburgerfest.ca', 'http://www.allamericananimalhospital.com/', 'http://www.spicessilverado.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', '1592500849', 'http://ilovenailspgh.wix.com/ilovenailspgh', 'http://www.sandsmotorstoronto.com', None, 'http://www.sevennumbers.com', 'http://www.mangotangonightclub.com', 'http://www.cafeccinos.com', 'https://www.joefresh.com/ca/', 'https://www.chick-fil-a.com/lakenorman', 'http://www.kingtandoori.com', 'http://genosgiantslice.com', 'http://www.tenthousandvillages.com/pittsburgh', None, 'https://www.casaagavemexicancuisine.com', 'http://www.brydenall.com', 'http://www.unioncoffeecompany.com', None, 'http://www.poolcarearizona.com', None, 'http://www.luxuryautobodys.com', 'http://www.cookout.com', 'https://www.le5e.cafe', 'https://f-n-js-beauty-bar.business.site', 'http://tibetkitchen.ca', 'https://locations.theupsstore.com/pa/gibsonia/410-north-towne-square?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://www.sergiosrestaurant.com', 'http://thebarwithnoname.ca/', 'https://www.paradisevalleyeyecare.com', 'http://www.shomalrestaurant.com', 'http://www.7-eleven.com/?yelp=29644', None, None, 'http://www.highlifeinc.com', None, 'https://www.kossacklaw.com', None, 'http://www.chiropracticlv.com', 'https://www.extraspace.com/storage/facilities/us/arizona/mesa/501578/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.rainbowdental.com/', None, None, 'https://stores.hallmark.com/pa/canonsburg/olivias-hallmark-shop-canonsburg-pa-11368.html', 'http://www.chelseagriloak.com', 'https://www.choicehotels.com/north-carolina/charlotte/econo-lodge-hotels/nc582/rates', None, 'https://locations.theupsstore.com/oh/fairview-park/21887-lorain-rd?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', 'http://www.thejoyofcleaningoc.com', None, 'http://www.starbucks.com/store/9298/', None, 'https://www.brasseriemelrose.com', None, None, 'http://www.wbpestcontrol.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/2371+East+Guadalupe+Street-Gilbert-AZ-85234/storeid=3272?cid=ps_ylp_2020', 'http://www.rubytuesday.com/', None, 'http://www.phoenixflowershops.com', None, None, 'http://superclassreflexology.com', 'http://www.mammaspizza.com', 'http://www.yardforce.ca', 'https://www.petsmart.com/stores/us/nc/wesley-chapel-store2110.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://famousmart.com', None, None, 'http://www.tommybahama.com', 'http://azeliteteam.com', 'https://www.clevelandcuriosities.com', 'http://www.clarksusa.com/eng/storeLocator/redirect.cfm?sectionID=b2c/storeLocator/storeLocator.cfm&displayStoreLocatorSearchResults=Y&var=d&ckey=US', 'https://www.choicehotels.com/pennsylvania/west-mifflin/comfort-inn-hotels/pa439/rates', None, None, 'https://www.marianetalbot.ca', 'https://www.mydailyjam.com', 'https://stores.joann.com/pa/pittsburgh/2053/', None, 'http://www.masterbacon.com', 'http://www.workingdraftbeer.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.mellowvibesdogtraining.ca', None, 'https://perry.zeppes.com', None, None, 'https://hottubhub.com', '1592501201', 'https://www.simon.com/mall/ross-park-mall', 'http://www.calvinklein.com', None, 'http://thornhill.wbu.com', 'http://www.407etr.com', 'https://hairenhancements.net', 'http://www.maidpro.com/tempe/', 'http://www.toronto.ca/parks/recreation_facilities/camping/index.htm', 'http://www.konapoke.com', 'http://fiveguys.com/', 'http://www.harlotshair.com', 'http://www.maxmusclephoenix.com', None, 'http://www.myoreckstore.com', 'https://www.alignology.com/chiropractor-las-vegas/', 'http://carolinadentco.com/', 'https://shop.nordstrom.com/c/spa-nordstrom-shop?utm_source=yelp&utm_medium=organic&utm_campaign=spas&utm_content=8380&utm_channel=lcl_brand_p&sp_source=yelp&sp_campaign=spas', 'http://www.cafe668.com/', '1592501269', 'http://grandempirebanquet.ca', 'http://wholesomemarket.ca/', 'http://vbarbershop.com/locations/arcadia-phoenix/', None, 'http://www.redmtnragdolls.com', 'http://www.autonationcollisioncenters.com/viewlocation.cfm?StoreID=74', 'http://saltysow.com/phoenix/', 'http://planetworkout.net/', 'http://www.macaronigrill.com/?utm_source=yelp&utm_medium=profile&utm_campaign=Phoenix--Ahwatukee', None, 'http://www.tempeparkview.com/?utm_medium=listing&utm_source=yelp', None, 'https://marketmalleyeclinic.com', 'https://www.tidedrycleanersaz.com/locations/chandler-blvd', 'http://www.scsbuildingandremodeling.com', 'http://www.newyorkfries.com/locations/view/89', 'http://www.tiremag.ca', 'http://www.sonicdrivein.com', 'https://www.meineke.com/locations/tn/madison-196/?utm_source=yelp&utm_medium=xvc', 'https://countrybrook.mgproperties.com', 'http://www.costco.ca/warehouse-locations/warehouse-1169.html?callingPage=WarehouseLocatorView&storeId=10302&BeginAddress=l5v1b4&langId=-24&location=l5v1b4&warehouseNumber=1169&catalogId=11201&numOfWarehousesToReturn=null', 'http://www.strosenh.org/locations/north-las-vegas/', None, 'https://www.pastamore.ca/acceuil', 'http://www.dynatelnv.com', 'http://www.chnv.org', 'https://stores.advanceautoparts.com/az/chandler/6170-w-chandler-blvd', 'https://www.amctheatres.com/movie-theatres/cleveland/amc-ridge-park-square-8?utm_uid=yelp', 'http://www.mtbmechanical.com', 'https://amobilenotary911.com', 'http://metrowb.com', None, 'http://wienerschnitzel.com/', None, None, None, 'https://www.target.com/sl/charlotte-midtown/2244', 'https://www.petpeoplestores.com/chagrin-blvd.-store.html', 'http://www.boxcarsocial.ca/', None, 'http://www.rosaccilawfirm.com/', None, None, 'http://revelationhairdesigns.com/', None, 'http://www.citydancecorps.com/', 'http://www.texasstation.com/dining/austins/?utm_source=YELP&utm_medium=SOCIAL&utm_term=TS&utm_content=TS-PROPERTIES&utm_campaign=TS-YELP', 'http://www.swagatbanquethall.com', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=103', None, 'https://www.famousfootwear.com/?partnerid=YELP', 'http://platformbeer.co/phunkenship', 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', 'http://www.angelinaspizza.com', None, 'http://www.fyodorbridal.com', 'http://www.arizonatmjpain.com', 'http://store-locator.barnesandnoble.com/store/2154', None, None, None, '1592501478', 'https://www.simonmed.com/locations/all/simonmed_imaging___mesa_desert_campus', 'http://www.bestbuyshuttersusa.com', None, 'http://www.santannailsspa.com', 'http://avanteproperties.com/residential-property/riva-apartments/', 'http://www.painturpeace.com', 'http://mamasboybbq.mdom.mobi', '1592501507', 'http://www.coldstonecreamery.com', None, 'https://stores.advanceautoparts.com/nc/huntersville/9924-knockando-ln', None, 'http://classysmokeshop.com/', 'http://www.safeguardproperties.com', 'https://raisingcanes.com/location/arizona/gilbert/coming-soon-gilbert', None, 'http://www.restocosmeticsurgery.com/', 'http://geauganuisancecontrol.com/', 'http://www.onemedical.com/phx/locations/kierlandcommons/?utm_source=yext&utm_medium=referral&utm_content=site_link&utm_campaign=localseo', 'http://lotrestaurants.ca', 'https://www.chronicinktattoo.com/locations/tattoo-shop/chronic-ink-markham-kennedy-denison/', None, None, 'http://www.peddlersson.com/', 'http://www.artsense.ca', None, 'http://www.abdconsignment.com', 'http://www.floordepotonline.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, None, None, None, None, 'http://peoplesrestaurant.site', None, None, 'http://sweetolenkas.ca', None, None, None, None, 'http://www.misterspas.com', 'http://www.veronanailsalon.com', 'http://libertymetals.com', 'http://www.pyramidtattoo.com', 'http://www.cameraworld.com', 'https://stores.sportsmans.com/sportsmans-warehouse/us/az/mesa/1750-s-greenfield-rd', 'http://www.cabanos.ca', 'http://www.flipflopworkshops.com', None, 'http://www.ohiocitypasta.com', 'http://mesaazlocksmiths.com', None, 'https://www.mattressfirm.com/stores/az/phoenix/mattress-stores-phoenix-az-85032-7927.html', '1592501673', None, 'http://bloomson9th.ca', None, None, None, 'http://5anddiner.com/', None, 'http://www.cloud9vegas.com', 'http://www.sweetceces.com/locations/broadview-heights/', 'http://dmvdrop.com/', 'http://thesicsense.com', 'http://www.redbarnriding.com', None, 'http://platinumaz.com', 'http://www.desertfamilywindowcleaning.com/', 'http://www.bathandbodyworks.com', 'http://www.acms.ca', 'https://mattressbyappointment.com/locations/az/chandler/', 'http://sincityindianmotorcycle.com', None, 'http://pizza.dominos.ca/Mississauga-Ontario-10348', None, None, 'http://spa810.com', None, None, None, None, 'http://www.clevelandheights.com/index.aspx?page=88', 'http://accurateconcreteleveling.com', None, 'http://www.tinttekmadison.com', 'https://www.bowlero.com/location/bowlero-gilbert?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'https://www.ttc.ca/Subway/Stations/Kennedy/station.jsp', 'http://www.icywakessurfshop.com', 'http://pvfamilymed.com', None, 'http://www.virtuebowling.com', 'http://parlour270.com', 'https://www.enterprise.com/en/car-rental/locations/us/sc/fort-mill-53b1.html?mcid=iyp:8368400', None, None, 'http://www.aramarkcafe.com/layouts/canary_2015/locationhome.aspx?locationid=4268', 'http://www.tammysbelleboutique.com', 'http://www.lamiragetempe.com/', None, 'http://centralphoenix.thecasualpint.com', '1592501814', 'http://www.dkvshair.com', 'http://www.haveaseat.ca', None, None, 'http://www.stlawrencemarket.com/shopping/vendors/olympiccheese.html', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.findlayvw.com/', 'http://northsidefloorcare.com/', 'https://dentist89103lasvegas.com', '1592501846', 'https://www.abuelos.com/restaurants/peoria/', 'http://www.autoglassboss.com', 'http://kingofwings.online', 'http://www.avondale.org/prld', 'http://www.WentworthHealthGroup.com', None, 'http://www.sukhothaifood.ca/parliament/', None, None, None, 'https://immediadent.com/locations/ohio/southland/', 'http://www.7-eleven.com/?yelp=29384', 'http://www.tenrenstea.com', 'http://www.bijoysrestaurant.com', None, 'http://breizhbistrot.business.site', 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', 'http://preciouspossessionsmoving.com/', 'http://www.melrosecalgary.com', 'https://www.kindercare.com/our-centers/phoenix/az/301312?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=301312', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.thairapysalonaz.com', 'http://www.engineeringforkids.com/las-vegas-west', None, 'http://velaapartments.com', None, None, 'http://www.uwveterinarycare.wisc.edu', 'http://www.libertytaxcanada.ca', None, 'http://www.destinationxl.com/mens-big-and-tall-store/storelocator/storeDetails.jsp?storeNumber=+9849', 'https://www.tacobell.com/food?utm_source=yelp&utm_medium=social&utm_campaign=yelp-pilot-test-menu-static-1-CS&utm_content=paid', 'https://arizona.weidner.com/apartments/az/phoenix/acclaim/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.couserortho.com/', 'http://www.klarityclinic.com', 'https://www.chevronwithtechron.com', 'http://lundimports.com', 'http://www.rickydavishair.com', 'http://www.insuringchampaign.com', None, 'http://www.alsonjewelers.com', 'http://www.jokerswildcasino.com/?disid=wmm_yelp_jw_corporate_jokerswildcasino_organiclink', '1592502002', 'http://www.thequiltingbee.net/', 'http://www.mazehcatering.com', None, None, 'https://www.clearviewfamilychiro.com', None, 'http://www.dreamcarrentals.com/', 'http://www.flowersofnevada.com', 'http://www.homeprideinspections.com', 'http://www.ahwatukeefoothillsmontessori.com', 'http://www.KristineBarone.com', 'http://www3.hilton.com/en/hotels/nevada/hilton-lake-las-vegas-resort-and-spa-LASLKHF/spa/index.html', 'http://www.bloomfielddrug.com', 'http://www.speedway.com', 'https://www.experiencethestandard.com', 'http://chatime.com/', 'https://www.t-mobile.com/store-locator/nc/charlotte/whitehall-corner?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.studioblueaquatics.com', 'https://www.planetfitness.com/gyms/north-scarborough?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.cotswolddentalcare.com', 'https://www.dollartree.com/locations/il/peoria/704/', 'http://www.winghouseandsportsbar.com/', None, None, 'http://www.jennifershairboutique.com', None, None, 'http://www.muttonheadstore.com/', 'http://www.clewoknroll.com/', 'http://thepalomino.ca', 'http://creamistry.com', 'http://canada.armaniexchange.com', None, 'https://www.firkinpubs.com/firkinonharbour/', None, 'http://www.point97.com', 'http://www.clemetparks.com/visit/index.asp?action=rdetails&reservations_id=1021', 'http://vecova.ca/social-enterprise/bottle-depot/overview/', 'http://trishnash.com', None, 'https://www.southparkperio.com', None, 'https://champsfamilyautomotive.com', 'http://www.enricos-shadyside.com', 'https://theeggworks.com', None, 'https://tandgconcepts.wixsite.com/tandgconcepts', 'http://www.sonorannews.com', None, 'http://www.gastonfoot.com', None, 'http://www.havenspa.net', 'http://www.normandyretirement.com', None, None, 'http://www.highnoterealty.com', 'http://www.ticktocktavern.net', 'http://www.eastcoastabs.com', 'http://www.highparktoronto.com/zoo.php', 'http://crispyairinc.com', 'http://www.trucomputers.com', 'http://www.fatbastardburrito.ca', None, 'http://www.themassagestudio.com', None, None, 'https://www.pizzeriaviamercanti.ca', None, 'http://www.ritasice.com', None, None, 'http://www.starbucks.com/store/15887/', None, 'http://www.picknpull.com', 'https://www.olliequinn.ca', '1592502237', 'https://notary.net/websites/notarysurpriseaz', 'http://www.mermaidfishandgrillhouse.ca', 'http://beautifulmedspalv.com', None, 'http://www.sassywink.com', 'http://www.abloommedicalspa.com', 'https://www.venezias.com/yelp-deals/', 'http://www.petsittinginphoenixandscottsdale.com', 'https://www.take5oilchange.com/locations/nc/gastonia-1011/', 'http://www.achievea-nu-yu.com/', 'http://www.nkdwax.ca', 'http://www.lakewoodplantcompany.com', 'http://www.thefourthmaninthefirepizzeria.com', '1592502290', 'http://www.rosendahlsappliancecenter.com', None, None, '1592502302', None, 'https://www.aldoshoes.com/ca/en/store-locator/store/1028', 'http://www.kostaandvics.com', 'http://www.bridgelanddentalcare.com', 'https://aboveaveragemoving.com', None, 'https://www.redmountainvet.com/?utm_source=yelp&utm_medium=social', 'http://strattonrvservice.com', 'http://weezianagumbo.com/', 'http://www.costco.com', 'http://www.iheartscout.com', 'http://www.letthemeatcakeaz.com/cupcake.htm', 'https://moxies.com/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', 'http://www.smartfixlv.com/locations/spring-mountain-location/', 'http://www.granbarkennels.com', None, 'http://www.jessebrown.com', None, None, 'http://www.sparksfamilymedicine.com', 'https://www.walgreens.com/locator/walgreens-132+richmond+st-painesville-oh-44077/id=5821', None, None, 'http://www.sheratonparkway.com/caesar-spa', None, None, 'http://www.snohice.com', 'http://www.cardinalfitness.com', 'http://www.twinsandcorealty.com', '1592502413', None, 'http://www.53.com', 'https://www.flatsatfoxhill.com/', 'http://certifiedmortgagebroker.com/vaughan', 'http://www.muralsusa1.com', 'https://majssalon.com', 'http://www.soccermaxx.ca', 'http://www.birddentistry.com', 'http://langertnetzband.com/', None, 'http://christiescabaret.com/christieclubs/clubs/phoenix', 'http://www.chapelhillmall.com', 'http://www.thestarksteam.com', 'http://www.whoafoods.com', None, 'http://uncommkt.com', None, 'http://www.benjaminsports.com/', None, 'http://www.crazyhorse3.com', 'https://mrsub.ca', 'http://treevalley.ca/', 'https://novelcoworking.com/locations/pennsylvania/pittsburgh/golden-triangle/', 'http://www.sdhqoffroad.com/', 'http://www.gooseisland.com/toronto-brewhouse/', 'http://www.papajohns.com', 'http://www.stacysatmelrose.com', None, None, 'http://www.infinitycustomglass.com', 'http://www.azcardinals.com', 'http://www.autoactionaz.com/locations-1321-n-dysart-road-avondale-az', None, 'http://www.totalbusinesssolutionsllc.com/', 'http://www.starbucks.com/store/10759/', 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', 'http://poohbearchildcare.com', 'http://thesparklebar.com', 'http://www.openhouseimports.com', 'http://www.thelearninglinq.com', 'http://taokitchen.wordpress.com', None, 'http://www.snugglebugz.ca/locations/etobicoke-baby-store', 'http://www.autobell.com/ab_locations/750-n-church-st/', 'http://tesloop.com', 'http://www.enchantedisland.com', 'https://www.donutshopbridgeville.com', '1592502582', 'https://www.outback.com/locations/nc/huntersville', 'https://smhwi.com', 'http://www.mainstreetautocenter.com', 'http://www.crestmontatballantyne.com', None, None, 'http://www.villafreshitaliankitchen.com', None, 'http://www.seethetrainer.com/', 'http://www.sanmoritzlv.com', None, None, 'https://www.cascadeloans.com/', '1592502622', 'http://www.richardsmapleproducts.com', 'http://toadnturtle.ca/location/airdrie', 'http://www.shopredrocketcoffee.com', 'http://www.gracklecoffee.com', 'http://www.thehumanbean.com', 'http://www.embuhair.com', 'http://www.gogitruck.com', 'http://www.tctwestproperties.com', 'http://www.menchies.com', 'https://www.thecapitalgrille.com/locations/oh/lyndhurst/lyndhurst/8060?cmpid=br:tcg_ag:ie_ch:dry_ca:TCGQ420LOCURL_dt:20200520_sn:yelp_gt:lyndhurst-oh-8060_pl:locurl_rd:1054', 'http://www.desertchryslerjeepdodgeram.com', 'https://www.rotorooter.com/lasvegas/', 'http://www.labcorp.com', 'http://www.timhortons.com/', 'http://www.aldoshoes.com', 'https://www.homesense.ca/en/storelocator?store=25', 'http://www.dukem.ca', 'http://www.johnnieschicagostylepizza.com/', '1592502688', 'http://www.clairvoyantkim.com/', 'https://ciaobistro.net', '1592502700', '1592502703', 'https://www.chick-fil-a.com/rossparkmall', 'https://delanomesa.com', 'http://fukuburger.com', None, 'http://www.crossroadsapartments.com', 'http://www.hoopssportsbarandgrill.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, 'https://local.biglots.com/nv/las-vegas/4500?zcp=pd_local_yelp', None, 'https://danduckworth.supremelending.com', 'http://www.monalisadental.com', 'http://www.acnpaintingllc.com', 'http://www.theartofcheese.ca', 'https://www.omnihotels.com/hotels/pittsburgh-william-penn?utm_source=yelp&utm_medium=sponsored&utm_content=PITDTN&utm_campaign=sponsored-website', 'http://www.3brotherspizza.net', 'http://www.carlosbarbershop.com', None, 'http://www.yongecollege.com', None, 'http://easymovingsolutions.ca', 'http://casinomontelago.com/index.html#/dining/', 'http://www.dannysfamily.com/', 'https://www.payless.com/stores-location/NV-LAS-VEGAS-5798.html', None, 'http://autorepairclinicaz.com/index.html', 'http://hairbyebony.yolasite.com', 'http://nailsspavillagecommons.com', '1592502807', 'http://www.ntb.com/store/6225/beachwood-oh-44122-4319?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'https://locations.panerabread.com/tn/cleveland/375-paul-huff-parkway.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://www.quiktrip.com', 'https://www.petsmart.ca/stores/ca/on/east-york-store0935.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', 'http://www.catskaraoke.com', None, '1592502829', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.trolleystopinn.com', None, 'http://www.24-7electricalservices.com/', '1592502850', 'https://www.get-go.com/', None, 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.chesterlandfamilydentalcare.com', 'http://www.freedomgunstore.com/', 'https://www.moes.com/find-a-moes/north_carolina/waxhaw/1050?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'https://www.psgdental.com/locations/precision-orthodontics-kent/', None, 'http://www.palmcroftchurch.com', 'http://www.centromotel.com', 'http://www.angelinaspgh.com/', 'http://www.marriott.com/hotels/travel/cmpfi-fairfield-inn-and-suites-champaign/', None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=2137&localechange=1', 'http://www.rossstores.com', 'http://www.danishpastryhouse.ca', None, 'http://www.minimightymutts.com', None, 'http://kellyslv.com/', 'https://www.bjs.com/cl/avon/0115', 'http://www.theicononcentral.com/the-icon-on-central-phoenix-az', 'https://kwiktow.omadi.com/user', None, None, None, 'http://www.cleancitycoinlaundry.com', 'https://twomenandatruck.com/movers/az/phoenix/north', None, None, 'http://www.northcoastdermatology.com', 'http://www.mapleside.com/', 'http://www.fitnesswest.ca', 'http://www.dominos.com', 'http://www.massageheights.com/gilbert', None, 'https://www.regencydermatology.com', 'https://www.metalsupermarkets.com/las-vegas-south', '1592503028', 'http://www.aepros.com', 'http://www.eliasnandk.ca', 'http://Www.drheidichiropractic.com', 'http://www.centrehonda.ca/', 'http://www.scottsdaledentistaz.com', 'http://www.vinceneilink.com/', None, 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', None, None, 'http://www.adesa.com/phoenix', 'https://lvfarmersmarkets.wixsite.com/lvfm/bruce-trent-park', 'https://www.ulta.com/stores/phoenix-az-108', 'https://www.truecoffeeroasters.com/', 'https://www.southstburger.com/location/st-clair-rushton/', 'http://www.tempeimprov.com', None, 'http://www.puttingedge.com/', '1592503087', 'https://www.nofrills.ca/store-locator/Joe%27s+NOFRILLS+Whitby/3141?storeId=3141', None, 'http://www.adrianscustompainting.com', 'https://stores.jcpenney.com/az/chandler/clothing-stores-chandler-az-0157.html', 'http://odysseytravelclinic.com', None, None, 'https://locations.theupsstore.com/nc/charlotte/2820-selwyn-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://gilbertps.schoolwires.net/valvistalakes', None, 'http://soffritto.ca', 'http://www.bullseyedieselperformance.com', 'http://www.arbys.com', None, 'https://www.barvegandale.com', 'https://cirquedusoleil.com/run', 'http://retail.purcelltire.com/contact/find-us/mode/3/6020-w-thunderbird-glendale-az-85306.aspx', 'https://www.truckaccessoriesindiantrailnc.com', 'http://www.ampm.com', None, 'http://www.cactusjacksauto.com', 'http://rascalhouse.com', 'http://mnconcordmills.com', None, 'http://Lakelasvegas.hilton.com', 'https://www.lidl.com/stores/US01163', '1592503175', 'http://www.allleakdetection.vegas', 'http://www.modernstairsandrailings.com', 'http://www.azspaws.com', 'http://www.opticausa.com', 'http://www.theurbantap.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', 'http://www.clubmonaco.ca', 'http://lvplasticsurgery.com/', 'http://boeufcochon.com', 'http://acquanailsalon.com', 'https://lasvegasliving.com/properties/positano/', 'https://www.dollartree.com/locations/az/phoenix/3684/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'https://massageworkscharlotte.com', None, None, 'http://haymakersportsgrill.com', 'http://hooterscasinohotel.com', 'http://www.jameselliot.com', 'http://www.milldental.com', 'http://www.pickeringtire.com', 'http://uncletetsu-ca.com', None, None, 'http://www.urologistlasvegas.com', None, None, 'http://www.ntb.com/store/8543/arnold-pa-15068-3507?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'http://www.saltroomlv.com', '1592503254', 'http://www.autolicenseplatesandframes.com', None, 'https://www.maximumrvstorage.com', None, None, 'http://www.blackbirdurbana.com', 'http://davidwhitefamilylaw.com/', None, 'http://www.calgarynailsalon.ca', 'http://www.rossstores.com', 'https://www.lusciousdessertstoronto.com', 'http://www.exxon.com', 'http://www.rbomotorsport.com', 'http://www.togosquare.ca', None, None, 'http://www.lcbo.com', '1592503297', '1592503299', None, None, None, 'http://guadalupenailspa.com', 'http://www.bikramyogatorontoeast.com/', 'http://www.vgah.ca', 'http://www.house15143.com', 'http://www.sonicdrivein.com', 'https://missionmedicalclinic.ca', None, 'http://www.bakkersironworks.com/', 'http://www.somersetnlv.org/', 'http://www.crepeitup.com', 'http://www.mikesbikechalet.com/', 'http://salonelle.ca', 'http://southernnevadaent.com/', None, None, 'http://www.houseofblues.com/cleveland/fr', 'http://www.fiveguys.com', 'http://www.majesticangelspa.com', 'http://www.thelittlegym.com', None, 'http://www.ricksrestorations.com/', 'https://www.wingstop.com/location/wingstop-734-south-euclid-oh-44118/menu', 'http://www.vegasvipcleaning.com', 'http://www.claimjumper.com', 'http://www.fiveguys.com', '1592503369', 'http://www.faceforwardaestheticsmesa.com', 'http://www.madchefgastropub.com', 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', None, None, None, None, 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', None, 'http://fuzzwaxbar.com', 'http://www.usfoods.com/about-us/chef-store/charlotte.html', 'http://www.academic-urology.com/', 'http://www.applewood-funding.com/default.asp', 'http://www.bornandglazed.com', 'http://www.phoenixeyebrows.com/hollywood-beauty-eyebrow-threading-at-mesa-riverview/', 'http://www.desertpest.com/', 'http://www.littlecaesars.com/', None, None, None, 'http://thebigcannoli.ca', 'http://www.awesomemachines.net', 'https://azsandwich.com', 'http://levinebros.ca', None, 'http://newmarketfishandchips.com', 'http://Lauracase.massagetherapy.com', None, 'https://haircutmentempeaz.com', '1592503439', None, 'http://www.fiestaparkapartments.com/?campaign_code=yelp_Fiesta_Park_AZ_85202', None, 'http://wineanddesign.com/northscottsdale', 'https://locations.panerabread.com/az/mesa/1946-south-signal-butte-rd.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://www.fatheads.com', None, 'http://www.planetsmoothie.com', 'https://cherylbrewermd.com', 'https://www.lillypulitzer.com/store/details/?StoreID=80228-225', None, 'https://locations.wendys.com/united-states/pa/west-mifflin/2280-lebanon-church-rd', None, 'http://www.onecentautosales.com', 'http://www.ripcurl.com/', 'http://copperstate.com/', 'http://www.zaratestudios.com/', None, 'https://www.ambientedge.com/henderson/air-conditioning-repair-company/', None, None, 'https://refreshclean.com', 'http://www.crawfordanddoyle.com', None, None, 'http://www.burlesqueaz.com', None, None, 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6100', 'http://www.sittonlocksmith.com', None, 'http://centralphoenixobgyn.com/', 'http://www.thecellgym.com', 'http://diamandauto.com', 'http://www.cuttingimagesalon.com/', 'http://www.scrappydogscooters.com', 'http://www.starbucks.com/store/9289/', None, 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', 'http://www.cvcheart.com', 'https://www.goodyearautoservice.com/en-US/shop/AZ/Mesa/000908243-85201-6821', 'http://www.pizzahut.com/', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://jj-handyman-service.business.site', 'http://www.aweddingonwheels.com/', 'http://www.oasismeadowsvegas.com', 'http://www.paradisemassageaz.com', 'http://www.oakvillenationalfitness.com/', None, None, 'http://popeyes.com', 'https://www.thebeachhouseaz.com', 'https://www.usps.com/', 'http://www.sensationalskin.com', 'http://www.quiktrip.com/', 'http://face.csdm.qc.ca', 'http://www.kingpizza.ca', None, 'https://www.bowmitsubishi.com', None, 'https://stores.cartier.com/united-states/az/scottsdale/7014-e-camelback-road', 'http://www.vegashomepainters.com', 'http://www.shopnofrills.ca', 'http://aznailschandler.com', 'http://www.lveyedocs.com', None, 'http://www.orangerealtygroup.com/', '1592503608', 'http://www.fourqueens.com', 'http://www.tsingtaospa.com', 'http://www.phovuho.ca', 'http://www.culvers.com/restaurants/avondale', None, None, None, 'http://www.childrensedationdentist.com', 'http://www.arborvillagecharlotte.com/?utm_knock=y', 'http://www.aquablueaz.com/', None, None, '1592503641', 'http://www.noesark.com', 'http://www.midas.com/pittsburgh/store.aspx?shopnum=6135&dmanum=688', 'http://www.stallingsrefrigeration.com', '1592503651', 'http://www.valeriotaxservices.com', 'http://www.sashabellaspa.com', 'http://www.miraclemileshoppingcenter.com', None, None, 'http://www.visionfinecars.com', 'http://arrowheadgastroenterologyassociates.com', 'http://bespokeyyc.com/', 'http://www.ipropertiesinternational.com', 'http://www.brightlightacademy.org', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, 'http://fiveguys.com/', None, 'http://www.thevaultwinestorage.com', 'http://www.truecoffeeroasters.com', 'http://www.allstoragevegas.com/locations/nevada/anthem', 'http://www.allmobilematters.com/stores/tempe-marketplace/', 'http://www.islanderapartments.com', 'http://www.elitek911.com', 'http://www.rolladenlv.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.meineke.com', 'http://my.clevelandclinic.org/locations_directions', '1592503713', None, 'http://www.timhortons.com', None, 'https://www.metro.ca/en/find-a-grocery/312', 'http://www.firepatio.com', 'http://www.edenparkrollerrink.com', 'http://www.eggsandmore.ca/', None, 'https://www.cosmopolitanlasvegas.com/opium/', None, 'https://poopydoo.com', None, '1592503745', 'http://altnbachs.com', 'https://www.prohockeylife.com/pages/store-vaughan-mills-ontario', 'https://www.aznaturalselections.com', 'http://www.southwestanimal.com/', 'http://www.cashmancrystal.com', 'https://www.ashleyfurniturehomestore.com/furniture-stores/united-states/nc/matthews/matthews?cmpid=2016YELP', 'http://leesliquorlv.com/locations/lake-mead-tenaya-2/', 'http://www.signingbydesign.com', 'http://www.montevistacleaners.com/', 'https://www.heinens.com/Heinens-of-Willoughby', None, 'http://www.bannerhealth.com/locations/scottsdale/banner-physical-therapy-95th?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', 'http://www.dunkindonuts.com', 'http://www.harrisburgfamilyphysicians.com', 'http://www.classicmovingservices.com/', None, 'https://stores.joann.com/pa/pittsburgh/2053/', 'http://www.quickfixcellular.com', None, 'http://www.buckandhoneys.com/monona', 'http://www.prettylittlesecrets.ca', 'http://www.poolagency.com', 'http://www.nativesunaz.com', 'https://www.loblaws.ca/store-locator/Glen+Erin+Drive%2C+Mississauga/1011?storeId=1011', 'http://truebelieverjiujitsu.com', 'http://ashtonsclassicbarbers.com', '1592503815', 'http://www.pauljohnsondrywall.com', 'http://www.taperformance.com/', None, '1592503826', 'http://www.thegentryswalkapartments.com', 'https://expressdd.com', 'https://acefamilychiropractic.com', 'http://www.katesonline.com', None, 'http://www.criminaldefenseattorneykg.com', None, 'http://www.blankcanvastheatre.com/', None, 'http://www.brownbagnow.com', 'http://www.berrygoodyogurt.com', None, 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2foh%2fcleveland%2fbeachwood-orange-place-south&sisearchengine=1524&siproduct=2748_Bus', 'https://www.canyonranch.com/las-vegas/', 'http://www.mitrahotyoga.com', None, 'http://aggieinc.net/', 'http://www.desertstorage.com/henderson-nv-self-storage', 'http://www.pictureperfectsmiles.com', 'http://yellowtaillasvegas.com/', None, None, 'http://kozycactus.com', None, 'http://www.whichwich.com', None, 'http://www.zeppes.com/', 'https://locations.visionworks.com/ll/US/AZ/Glendale/7700-W-Arrowhead-Towne-Center', '1592503899', 'http://www.sandysrestaurant.ca', 'http://www.nandos.ca/restaurants/calgary', None, 'http://skyetechexteriors.com/', 'https://www.advantagegrandcanyon.com', 'http://hairdesignco.com', 'http://www.maidpro.com/phoenix-central', None, None, 'http://www.koryblythedds.com/', 'http://www.foodlion.com', 'http://www3.ttc.ca/Routes/63/Northbound.jsp', None, 'http://www.taekwondo.ca', None, 'https://locations.nekterjuicebar.com/ll/US/OH/Brecksville/8215-Chippewa-Road?utm_source=yelp&utm_medium=link&utm_campaign=Brecksville&utm_content=URL', 'http://www.theedgesalonaz.com', 'http://www.touchofhealing.net/', 'http://www.cmacsaquarium.com', 'http://www.agentswithoptions.com', 'http://www.a-agents.com', 'http://www.vivablowout.com/', 'http://thetimeshop.com/index2.html', None, 'http://www.gautamadine.ca', None, 'http://www.mckennateam.com', 'http://empiretechrepairs.com', 'http://www.apexauto.ca', 'http://www.newbornangelcare.com', None, None, None, 'http://www.mrsub.ca', None, 'http://www.hollingsworthroofing.com', 'http://www.thecommonerpgh.com/the-commoner-corner/?utm_source=yelp.com&utm_medium=business+listing&utm_campaign=profile+url', 'http://www.sitstaypet.net', 'http://www.MagnusSportsUSA.com', 'https://www.ihop.com/en/restaurants/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', 'http://www.bankofamerica.com', 'http://www.acupunctureshiatsu.ca', None, 'http://soraethiopianrestaurant.com', 'https://thedefenders.net', 'http://azpropertybrokerage.com', None, None, 'http://crownstationpub.com', 'http://downtownlumber.com', None, None, None, 'http://www.arbys.com', None, 'https://avapgh.wordpress.com/', 'http://www.jiffylube.com', 'http://www.unicornballoon.com/arizona.htm', None, 'http://www.greatclips.com/', None, 'https://www.wellsfargo.com', 'http://georestorationaz.com', 'https://www.frysfood.com', 'https://www.phoenix.edu/redflint.html', 'http://yourlasvegasbroker.com/', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.hcpnv.com/providers/matthewbarton/', 'http://irwincycles.com', 'http://phillyssportsgrill.com/', None, 'http://rodneysrestaurant.com/', 'http://www.globesalon.com', 'http://pizzabobs.ca', None, 'https://goo.gl/oq2f2R', 'http://www.homevilletrolleystop.com', 'http://www.francescabakery.com/', None, None, 'http://www.calgary.ca/CSPS/Recreation/Pages/Golf-courses/Confederation-Park.aspx', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://www.gnc.com', 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', 'http://www.lobstersalute.com', None, 'http://www.filibertos.com', 'http://www.verizonwireless.com/stores/pennsylvania/monroeville/monroeville-204206/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.gojima.ca', 'http://www.totalgerman.com', 'http://elitegaragedoorsystems.com', None, '1592504135', 'http://forevertruetattooaz.com', None, 'http://www.americanflyers.net/schools/arizona/default.htm', None, None, None, None, 'http://www.cockroachtheatre.com', 'http://perfectcarpetcleaningpittsburgh.com', None, 'https://www.amazinglashstudio.com/studios/az/chandler/chandler-mall', 'https://www.sprouts.com/stores/details/-/store-details/view/store/5/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://www.peets.com/?cm_mmc=yelp*peets*8_28_12_homepage*na', '1592504169', 'http://greenleafartsdistrict.com', 'http://www.mirabellalux.com', 'http://go.georgestreetphoto.com/l/9752/2014-06-04/m1825', None, 'https://www.valuecityfurniture.com/store-locator/oh/warrensville-heights/4095-richmond-road', None, None, 'https://www.staples.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://shanebakerstudios.com/', 'http://www.lvsurgical.com', '1592504197', 'https://locations.planethollywoodintl.com/us/nv/las-vegas/3500-s-las-vegas-blvd', 'http://www.layersoflovely.com', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', '1592504209', 'http://authenticpizzadeli.com', None, None, 'http://www.cabrera-appliance.com', None, None, None, 'http://www.nchinc.com', 'https://skincitylaser.com', 'http://www.darbyacresfarm.com', 'http://www.popdrinkslv.com', 'https://www.batteriesplus.com/store-locator/nv/lasvegas/batteries-plus-327?utm_source=yelp&utm_medium=local&storecode=327', None, None, 'https://www.goodnightpeds.com/locations/peoria-az/northwest', None, 'http://www.hapabrows.com', 'http://www.sundaeartgallery.com', 'https://www.americancampus.com/student-apartments/wi/madison/the-james', 'http://www.flightnetwork.com', '1592504258', 'http://www.scaddingcourt.org/', 'http://www.goodfellowmovers.com', 'http://www.rockler.com/retail/stores/az/phoenix-store', 'https://groundxcontrol.com', 'https://www.regmovies.com/theatres/regal-medina/0707?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Medina', 'http://www.mcdonalds.com', None, None, None, None, None, 'http://www.dantespizza.ca', None, 'https://www.alamo.com/en_US/car-rental/locations/us/phxt71-phoenix-sky-harbor-international-airport.html?mcid=iyp:8368400', 'http://www.pizzapizza.ca/', 'https://www.lifetimefitness.com/spa/spa-salon.html?utm_source=yelp&utm_medium=directory&utm_campaign=BCH-acquisition', 'http://buffalowildwings.com', None, 'http://www.psychicreadingslasvegas.com', 'http://www.tazcooks.com', 'http://www.improvecanada.com', None, 'http://www.21stcenturyneurology.com', None, None, 'http://cntskinandlaser.com', 'http://locations.in-n-out.com/160', 'http://www.7forallmankind.com', 'http://www.tasteofthai.co', 'http://www.wholefoodsmarket.com/stores/pittsburgh', 'https://lvtaco.com/home', None, 'http://www.dailoto.com', 'https://www.sleepcountry.ca', 'http://mortonslv.net/', None, None, 'https://website-1352051195390416663140-barbershop.business.site', 'http://www.ccrealtyhomes.com', 'http://www.joann.com', 'http://eggstasyaz.com', '1592504352', 'http://www.kandbgaragedoors.net', 'http://www.hideaway-usa.com/', 'http://www.papamurphys.com', 'https://organiccleanersaz.com/organic-dry-cleaners-and-laundry-phoenix/', 'http://www.innovativecosmeticsurgery.com/', 'http://www.azprogroup.com', 'http://www.bonbreads.com/index.html', 'http://eyetique.com', 'http://xiaozhuzhu.ca/', None, 'http://www.ezexteriors.com', 'http://www.glendalepediatrics.com', None, None, None, 'http://www.eastvalleyshuttleservice.com/', 'http://www.vancleefarpels.com/', 'https://airtechradon.com', 'http://saje.ca', 'https://www.anytimefitness.com/gyms/2195/Richmond-Hill-ON-L4E-3L6/?utm_source=yelp&utm_medium=local', None, '1592504406', 'http://drhelenk.com', None, None, None, None, 'http://www.villageatbrierfield.com', 'https://ribfestmississauga.com', 'http://onestopnutrition.com', None, None, None, None, None, '1592504436', None, 'http://www.deltaco.com', 'http://www.brgroomer.com/', None, 'http://www.theartofshaving.com', 'http://www.chefsilvana.com', None, 'http://www.KeylessShop.com', 'http://www.allstardrywallandpaintingaz.com', None, 'http://organicnailbar.ca', 'http://www.shell.com/', 'http://www.avocachocolates.com', None, None, 'http://alwaysamazingtaxiandlimo.business.site', 'http://djhollywoodspizzaandgyro.com', 'http://www.integrityfirstrealtyaz.com', '1592504483', 'http://trioristorante.com', None, 'http://www.somacalgary.com/', 'http://www.waunabowl.com', 'https://www.youfit.com/gym/phoenix-32nd-st-7406', 'http://www.mariosauto.ca/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLTBL', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.purehealthfoodslv.com', None, '1592504513', '1592504516', None, 'https://lakeshorearena.ca', 'http://www.eagleplumbing.net', '1592504527', 'http://www.wendys.com/', None, 'http://www.portofsubs.com', None, '1592504539', 'http://nvtlaw.com', 'http://www.paintcabin.com', 'http://drainrescueplumbers.com', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', 'http://coppervalleypainting.com', 'http://www.drblazer.com', '1592504557', None, None, None, None, 'http://marcelinasfilipino.wix.com', None, None, None, 'http://kingsfamily.com/?utm_source=yelp&utm_medium=referral', None, 'http://miguelslandscapinginc.com', 'http://www.plus15.ca', 'http://www.caplanskysdeli.com', 'http://www.cafecarumba.com', 'http://www.planetfitness.com/gyms/mesa-az-806?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.torontometrolocksmith.com/', None, '1592504598', 'http://www.maddysfattys.com', None, None, 'https://americaontap.com/event/madison-on-tap/', 'http://www.whitespot.ca/', 'http://www.canteentequilabar.com', 'http://www.imagineaudiovideo.com', 'http://aussieheatlv.com', 'http://www.oasispoolslv.com', 'http://www.SimplyScuba.VEGAS', 'http://losgirasolesgrillandbar.com', 'http://www.allegromusic.ca', 'http://jackastors.com/location-map/22/', None, 'http://www.marriott.com/hotels/travel/phxcb-jw-marriott-scottsdale-camelback-inn-resort-and-spa/', 'http://www.thedesignercookie.com', 'http://ldvpizzabar.com', 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', None, 'http://topsummerlindentist.com', 'http://www.lasvegastransmissionco.com', None, None, 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://pavaomeats.com/deli/deli-meats/', 'http://www.camelliaweddinggown.com', None, 'https://www.mcdonalds.com/ca/fr-ca.html', None, 'http://www.crafteddecor.ca', None, None, None, 'http://www.lindsayfricks.com', None, 'https://www.tricorefit.com', 'http://www.filibertos.com', None, 'http://starcrestcleaners.net', 'http://www.boccaonbaldwin.ca/', 'http://spraytanqueenstudio.com', 'www.saharacalgary.com', None, 'https://www.goodwillaz.org/location/dysart-thunderbird/', 'http://antojitosguayabitossunrisemanor.mybistro.online', None, 'http://www.oneworldtile.com', None, 'http://www.elmocambo.com', 'http://www.auntieannes.com/locations?addressline=Las+Vegas%2C+NV+89109', 'http://www.kentsunsations.com', 'http://werejuvenate.com', 'http://locations.tccrocks.com/az/phoenix/7611-w-thomas-rd.html', 'http://alphillipslv.com/', 'http://www.pricechopper.ca/', None, None, None, None, 'http://brittanysdogsalon.myonlineappointment.com', None, 'https://carylbakervisage.com/pages/toronto-eaton-centre', 'http://www.discounterspoolandspa.com', None, 'http://elements.henderson-nv.net', 'http://www.meekbleekfitness.com', None, 'https://levinehearing.com', None, None, 'http://www.lindsaylou.com/', 'http://www.theapplexchange.com', 'http://www.lubestop.com/Locations/Parma-II', 'http://www.mclintockbuilders.com', 'http://www.hortfrontiers.com', 'http://stores.toysrus.com/nc/concord/toy-store-concord-nc-8825.html', None, 'http://hogfathersbbq.com', 'https://www.olivegarden.com/locations/pa/monroeville/monroeville-mall/1148?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:monroeville-pa-1148_pl:locurl_rd:1100', '1592504820', None, 'http://www.tjmaxx.com', 'http://www.innersagewellness.com/', None, '1592504834', None, 'http://www.petguardsclinic.com', 'http://vipguest.vegas', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.doubledouble.ca', None, None, None, None, 'http://fullcirclepizza.ca', 'http://www.mainstreetcasino.com/vegas-hotel-reservations?disid=wmm_yelp_ms_corporate_mainstreetstationcasino_organiclink', 'http://www.mipueblomexgrill.com', None, 'http://www.masterodorremoval.com', None, 'http://aureliospizza.com', 'http://drgv.net/', 'http://www.theframeartist.com/', None, 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.calgaryphil.com', 'http://jays-diner.com/', None, 'http://www.domainhenderson.com', None, 'http://www.gardenofenglandflowers.com/', 'http://www.bankofamerica.com', 'http://www.gasperspizza.com/', 'http://www.landscapevegas.com', None, None, '1592504937', 'http://www.mysantropezapartments.com/', None, 'http://www.madebycustom.com', 'http://listenhearsmarthomes.com', None, None, 'https://www.maps4u.com', None, 'https://www.peterpiperpizza.com/locations/tempe-az/baseline-mcclintock', None, 'http://www.derados.com/', 'http://www.stevesoffa.com', 'http://www.lakewoodpubliclibrary.org', 'https://www.allseasonsretractables.com', 'http://seattle-espresso.com', None, 'http://www.southhillsbrewing.com/', 'http://www.sculptfitnesstraining.com/', 'http://www.honefitness.com/', 'http://www.toonseum.org/', 'http://www.mtaxes.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://coopwinesandspirits.com/events', None, 'http://www.villagepizzategacay.com', 'http://www.rockysmadison.com', 'http://pittsburgh.pirates.mlb.com/pit/ticketing/lexus.jsp', '1592505031', 'http://www.hublot.com', None, 'http://coyleauto.com', None, 'http://www.tatumeyecare.com', 'https://www.desjardins.com/fr/votre_caisse/coordonnees/index.jsp?transit=81530323#74998', 'http://sevenhillssc.com/', '1592505057', 'http://www.lepeep.com', 'http://www.theartofnakedyoga.com/', None, None, 'http://www.saborcharlotte.com', 'http://www.olympicflamerestaurant.com/', 'http://www.staystudio6.com/reservations/motel_detail.aspx?num=5061', 'http://pedinnailsnewmarket.com', None, 'http://www.sumilicious.ca', 'http://www.billabbottgm.com', 'http://www.kolorphx.com/', 'http://www.county.allegheny.pa.us/parks/scfac.aspx', 'http://www.157lounge.com', None, 'http://www.teashop168.ca/', 'http://www.lowes.com', None, 'http://www.clevelandhousekeepers.com/', None, None, 'http://www.krispykreme.com', 'http://www.atlanticondundas.com/', 'http://my.clevelandclinic.org/locations/directions/439-falls-family-practice--western-reserve-hospital', 'http://www.summitphysique.fitness/', None, 'http://www.kinggalleries.com', None, 'http://www.tambalounge.com/', 'http://www.nchomeimprove.com', 'http://www.interstatetowing.net', None, 'http://azofs.com/about-us/', 'http://www.deltaco.com', None, None, 'http://couriergraphics.com', None, None, 'http://www.pumponrathburn.com', None, 'http://phoenixuu.org/', 'http://www.superchargedelectric.com', None, 'http://www.southhillsmower.com', 'http://www.menchies.com', 'https://www.extraspace.com/storage/facilities/us/arizona/chandler/1000000272/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.tildetaco.ca', 'http://metrodiner.com', 'http://www.healinghandsmassageaz.com', None, 'http://www.psychicsessionsoflasvegas.com', 'http://fiveguys.com', 'https://www.t-mobile.com/store-locator/nc/huntersville/sam-furr-rd-birkdale-commons-pkwy?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.superstarcarwashaz.com/fullservice.php', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://distresscentre.com', 'http://www.urbantreesalvage.com', 'http://www.eggsquis.com/fr/restaurants.php?restaurant=brossard', 'http://www.cimarronspa.com', 'https://www.haircutmenparktowncharlottenc.com', 'https://groovylifeunlimited.com', 'https://gravityfinance.com', 'https://integrativehealinglv.com', 'http://www.opticaltrust.com', None, None, 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.mikescompleteautoservice.com', None, 'https://locator.bmo.com/default.aspx?t=hb', None, 'http://eastvalleyfansandblinds.com', None, 'http://www.wisebar.ca', None, 'http://www.husamiacupuncture.com', None, 'http://www.cleantownusa.com', None, 'http://www.ballsoffun.ca', None, 'http://www.harvesthillsauto.ca/', '1592505332', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.amazonaquarium.tumblr.com', 'http://www.chandhrathai.com', 'http://ad.doubleclick.net/clk;266326037;92222803;c?http://www.24hourfitness.com/FindClubDetail.do?clubid=205&edit=null&semiPromoCode=null&cm_mmc=Yelp-_-ClubPage-_-BusinessListing-_-Link', 'https://www.carvana.com', None, 'https://www.bossmoveaz.com', '1592505363', 'http://www.kangaroobounceparty.com', 'http://www.starbucks.com/store/9229/', 'http://platosclosetscottsdale.com/', 'https://www.theplumberguy.com', None, None, 'http://canadasbakingandsweetsshow.com', None, 'https://www.la-viena-calgary.com', None, 'https://www.qualitybumper.com', 'https://phoenixphreshcafe.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/13956+Cedar+Road-University+Heights-OH-44118/storeid=3347?cid=ps_ylp_2020', None, 'http://www.redwokbuffet.com', 'http://koalasleepcenters.com/phoenix-biltmore', None, 'http://www.myrotiplace.com', None, 'https://www.ihg.com/holidayinn/hotels/fr/fr/laval/ymqlv/hoteldetail', 'http://www.drake.legal', 'https://www.xyzstorage.com/locations/scarborough/?utm_source=yelp&utm_medium=Directory&utm_campaign=yelp_Listing_Scarb', 'http://www.myteaz.com', None, None, None, 'http://www.meridianhall.com', None, 'https://tozzilv.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.purcelltire.com', None, 'http://crookschiropractic.com', 'http://www.gianteagle.com', 'https://www.audigilbert.com', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.burntwoodtavern.com/burntwood-tavern-chagrin-falls/', None, None, 'http://stores.partycity.com/pa/pleasanthills/party-store-pc662.html', 'https://www.mec.ca/en/stores/north-york', None, 'https://www.signaturestyle.com/locations/wi/sun-prairie/cost-cutters-market-place-at-sun-prairie-haircuts-17732.html', 'https://www.cricketwireless.com', 'https://www.ohdentalcare.com', 'http://www.desertspringspools.online', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.mightyfinedetailingservices.com', 'http://airiteac.com/', 'http://www.brawleysbeverage.com', 'http://www.hesselparkdentistry.com/', 'http://www.cobsbread.com', 'http://www.spectrummedgroup.com', 'http://www.mcosmiles.com/markham-office', None, 'http://www.dinopalmierisalon.com', 'https://www.foxrentacar.com/en/locations/united-states/nevada/las-vegas-airport.html', 'http://www.thedancerspointe.com/', 'https://locator.chase.com/nv/las-vegas/6460-sky-pointe-dr?jp_cmp=rb/LocalListings/aff/branch/na', None, 'http://crazyivans.menu', 'http://www.alohahomes4rent.com', 'https://www.sprint.com/storefronts/bd/sprint-fairlawn-oh-44333-fcs-873/?ecid=SEO:Yelp:2020_Q1:LastMile', 'https://charlottepride.org', 'https://cabinfive.com', 'http://www.marjonceramics.com', 'http://cpisecurity.com/service-area/charlotte-nc/?utm_source=yelp.com&utm_medium=referral&utm_content=charlotte', 'http://www.lennar.com/New-Homes/Nevada/Las-Vegas/Henderson/Heritage-at-Cadence?utm_source=Yelp&utm_medium=Social&utm_campaign=CORPLEN_Yelp_Listings', None, None, None, 'https://probrakes.com', 'http://goubuli.ca', 'http://www.starbucks.com/', 'http://drleobiglaiser.com/', None, None, 'http://www.casadecorplus.com', 'http://www.vegasbodyworks.com', 'http://info.abcmotorcredit.com/abc-motorcredit-bedford-ohio-used-car-dealership-0', None, 'http://berniesbeads.com', None, '1592505668', None, 'http://www.fireduppottery.com/', 'https://www.jerseymikes.com/3096', 'http://Www.gracespavegas.com', 'http://www.yelmwood.ca', 'http://www.freshandwild.ca', None, 'http://www.globeparking.com', 'http://www.restaurantnoca.com', 'http://www.stridesrunning.com', None, 'http://www.oldemeckbrew.com/', 'http://www.mckenneyproperties.com', 'https://www.petsmart.com/store-locator/store/?storeID=2518&utm_source=Yelp&utm_medium=cpc&utm_campaign=storelocator', 'http://sexyvegasskin.com/', None, 'https://www.cubesmart.com/arizona-self-storage/tempe-self-storage/199.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'http://www.futureshop.ca/', None, 'http://www.vet905.com/your_pets.html', 'http://locations.oreillyauto.com/az/surprise/13710-west-waddell-road.html', None, None, 'http://www.ice-q.com', None, 'http://www.techcitycanada.ca/index.php?id_cms=7&controller=cms', None, 'https://www.radisson.com/akron-hotel-oh-44321/akron', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.katohospital.ca', 'https://www.lifeatlomavistaapartments.com', 'https://nativegrillandwings.com/location/avondale/?utm_source=Yelp&utm_medium=Local&utm_campaign=Avondale', None, 'http://www.acupuncturelasvegas.com', 'http://www.eutopiafit.com', 'http://homeenvisionsllc.com', 'http://www.willowlakepark.net', 'http://www.salonlevel6.com', None, None, 'http://lasvegas.carenow.com/location/arby-durango', 'https://www.thompsonhotels.com/hotels/canada/toronto/thompson-toronto/restaurants/thompson-diner?utm_term=thompson-diner&utm_content=homepage&utm_medium=media&utm_source=yelp.com&utm_campaign=business-listing', 'http://www.meeplemart.com/', 'https://www.joefresh.com/ca/', None, 'http://www.sundevilfire.com', 'http://chinasea.ca', 'http://www.eyelashofluxury.com', None, None, None, 'http://www.cosmickidsdental.com', 'http://foxykickboxing.ca', 'http://www.big5sportinggoods.com', None, 'http://www.rheesacupuncture.com', 'http://www.dhamadison.com/locations/south-clinic', 'https://www.criminallawyerslasvegas.com', 'http://www.southland.ca', 'http://www.fourseasons.com/lasvegas/spa', 'http://www.wedgebar.com', 'https://www.littlevillagemh.com', 'http://www.pillerchilddevelopment.com', None, None, None, 'https://horizonairlv.com', None, None, 'http://www.arizonasbestdds.com', 'http://www.billsandson.com', 'http://complete-drycleaners.com', None, None, None, 'http://grampaspizzeria.com/', 'http://www.beebeplumbing.com', 'http://www.minitlube.com', None, 'https://www.eyecontactmadison.com/locations/eye-contact-madison-west.html', 'http://www.gangseirealestate.com', 'https://www.cfcare.org/', None, 'http://www.smithsfinerugcleaning.com', 'https://www.hybikes.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700006430431399&ds_s_kwgid=58700000444952566&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.edwardlevesque.ca', 'http://www.blockbistro.org/', 'http://www.udipicharlotte.com', None, None, 'http://www.carebearpreschool.com', 'https://www.psgdental.com/locations/precision-specialty-south-hills/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.whimsicalpigbedandbreakfast.com', None, None, 'http://local.firestonecompleteautocare.com/ohio/cleveland/6874-pearl-rd/?lw_cmp=IYP_YPC_MLP_1694', 'http://www.valleymarinearizona.com/', 'http://www.rossstores.com', '1592506014', 'http://accelerated-fitness.com', 'https://www.kitchenremodelerscottsdaleaz.com', None, '1592506026', '1592506030', None, None, 'https://elsupermarkets.com/mesa-1251-e-southern-ave-az-85204/', 'http://www.nowplumbingservices.com', None, None, 'http://www.marriott.com/hotels/travel/phxrp-residence-inn-phoenix-glendale-peoria/', None, 'http://www.serrv.com', 'http://www.azoasispools.com/', 'https://nationalfirstresponse.com', 'http://www.4naturesfinest.com/', 'http://www.greenvalleyveterinarians.com', 'http://www.theyogahangout.com', 'http://orientaljadeye.com', 'http://www.thesimplegreek.com', 'http://www.star1personnel.com', None, 'http://www.arbys.com', 'https://www.amazinglashstudio.com/studios/az/phoenix/norterra', 'https://locations.usbank.com/index/arizona/phoenix/west-bell-rd-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.werentaz.com/', 'https://www.ethanallen.com/on/demandware.store/Sites-ethanallen-us-Site/en_US/Stores-Details?StoreID=473&utm_source=yelp&utm_medium=organic&utm_campaign=unpaid_listing&utm_term=473', '1592506118', 'https://local.fedex.com/nv/las-vegas/office-1441/', 'http://www.poolwerx.com/locations/arizona/pool-shop/higley-pecos-gilbert-pool-supplies-services', None, None, None, 'http://desertcardio.com/dr-zia-u-khan', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, None, 'http://www.bigotires.com/regions/Nevada', 'http://savvysilvers.com', 'http://www.jakprints.com/', 'http://www.lasvegascookingexperience.com', 'http://pulpjuiceandsmoothie.com', 'http://www.fieldslegalservices.com', None, 'http://www.la-mill.com', 'http://www.pizzahousebakery.com', 'https://www.walmart.com/store/1788/scarborough-me/whats-new', 'http://www.ampm.com', 'http://www.pantryfoods.ca/', 'http://endocrineclinic.net', 'http://maerowitzlaw.com', 'http://www.peaceloveandlittledonuts.com', 'http://www.resifenceinc.com', 'http://www.azpartybusrentals.com/', None, None, 'http://www.sistershome.net', None, 'http://www.racewaycarwash.com', 'https://amazingtint.com', 'http://www.allegromusicaz.com', 'http://www.mariachidemexico.com', 'https://www.choicehotels.com/CN749?mc=blypypaf', 'http://www.wolffkubly.com', 'http://kingchefcuisine.com', None, 'http://www.halecoffee.com', 'http://www.spawest.com', 'https://www.choicehotels.com/ohio/akron/econo-lodge-hotels/oh541/rates', 'http://www.paramountfinefoods.com', 'http://www.baklawaking.com/', None, '1592506281', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.torontoluckymaids.com', None, 'http://www.fusionchiropractic.ca', None, 'http://www.thewexlerapartments.com', None, None, 'http://coolfishlkn.com', 'https://www.carolinashealthcare.org/locations/Weddington-Family-Medicine', 'https://my.clevelandclinic.org/locations/rejhc', 'https://locations.theupsstore.com/az/mesa/2753-e-broadway-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://neurologyassociates.com/clinic-locations/chandler-az-clinic/', None, 'http://www.gentledentaltempe.com', 'http://www.palmeastern.com/?cid=YP.DM.1009', None, 'http://www.frankspizzachicken.com', None, 'http://www.visionsource-drdaviseyecare.com', None, None, 'http://www.vitospizzatruck.com', 'http://www.cardenalcarstereo.com', None, 'http://locations.traderjoes.com/pa/pittsburgh/638/', 'http://jandgshoerepair.com', 'http://lastexitlive.com', 'https://www.reddevelopment.com/shops-at-norterra/', 'http://goldenskulltattoo.com', None, None, 'http://6ixlaw.ca', 'https://www.wilhelmautomotive.com/locations/goodyear/', 'http://www.shredcolv.com', 'http://www.starautomotiveinc.weebly.com', None, 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'http://www.foothappyspa.ca', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', 'http://www.ibrowthread.com', 'http://www.monaghanautorepair.com', 'http://www.reebokcrossfitcharlotteuptown.com/', 'http://aquariussalon.com', 'http://www.starbucks.com/store/14887/', 'http://www.voguebistro.com/', 'http://beauty-plus-nail-spa.business.site', 'http://www.backpainfix.com/', 'http://www.avvegas.com', 'https://showgrow.com/locations/las-vegas/', 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'http://www.pitapitusa.com', 'http://www.lesainttropez.com', 'http://www.smile4ucharlotte.com', None, 'http://www.madisonbrows.com/', 'http://www.liveatsait.com/', 'http://www.wynnfitness.com/location/toronto-west', None, 'https://stores.savers.com/on/brampton/valuevillage-thrift-store-2030.html', 'http://clickserve.dartsearch.net/link/click?lid=43700044281388230&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://elitepropertieslasvegas.com', 'http://www.gustopizzaria.ca', None, 'https://www.mrhoneydoservices.com', 'http://www.celebritytanning.com', 'http://gisoosalon.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://comfortfootworks.com', None, '1592506537', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.hungryhowies.com/store/hungry-howies-00610?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=610&utm_content=Website_Link', 'http://lafleurfloralboutique.com/', 'http://www.sutrastudios.com', '1592510727', 'http://www.vippoolandbar.com', 'https://www.monicals.com/locations/monicals-pizza-of-urbana/', 'http://www.arizonasbestenglishbulldogs.com', 'https://bthejeweleronline.com', None, 'http://redrockrefrigerationaz.com', 'http://www.mastercleaners.us', None, None, 'https://drafthouse.com/phoenix/theater/chandler?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp-page&utm_content=businessurl&utm_term=phoenix', '1592510767', 'https://locations.nekterjuicebar.com/ll/US/AZ/Glendale/20022-N_-67th-Ave_?utm_source=yelp&utm_medium=link&utm_campaign=Arrowhead-Lakes&utm_content=URL', None, 'http://www.thepint.ca/calgary/', 'https://locations.cibc.com/on/toronto/03902?q=Toronto%2C+ON+M4K+1P7&loc=M4K+1P7%2C+ON', None, 'https://www.thedentureexperts.com', None, None, 'http://www.raymervillebakery.ca', 'https://www.suburbanpropane.com/locations/las-vegas-nv/?utm_source=yelp&utm_medium=organic&utm_campaign=contact', 'http://phxmastermover.com/', 'http://www.tastyyo.com', 'http://www.zuccas.ca', '1592510817', 'http://poorjohnscafe.com/', 'http://o48realty.com', None, None, 'http://www.faceeffectsbyjodi.com', 'http://www.shopsquareone.com/stores/sq1-cultures', 'http://www.chaircoverscheap.com', None, 'http://www.roseandsons.ca', 'https://www.aritzia.com/en/store?StoreID=1319', 'http://iceberglogistic.ca', None, 'http://www.slounge.ca/', 'http://www.happytownplaycentre.com', 'http://opticalexpressionsaz.com', None, None, 'http://www.comicsandfriends.com', None, None, None, 'http://www.epennzoil.com', None, None, 'http://www.caravantaproom.com', 'http://www.pghpsychotherapy.com', 'http://www.baybreezevegas.com/index.aspx', 'http://www.biotopesante.com', None, 'http://apexkarate.com', 'https://www.pediatricdentalsouth.com', 'http://www.landmarkcinemas.com/en.aspx', 'https://locations.visionworks.com/ll/US/AZ/Avondale/10285-West-McDowell-Rd', None, 'http://www.club-doggie.com/', None, None, None, 'http://www.kingdomhome.com', 'http://www.mcfarlane.com', None, 'http://www.nativebloomlandscape.com/', 'http://www.dunkindonuts.com', 'http://wrgautobodycollision.com', '1592510974', None, 'http://ultraskinwaxcenter.com', None, 'http://www.plazaapplianceservice.com', None, 'http://www.mikesdeliandbagels.com', 'http://www.sonicdrivein.com/', 'http://www.orangetreeimports.com', 'https://www.originaljoes.ca', None, 'http://www.gamestop.com', 'http://www.alpinemc.com/lasvegas', 'http://www.modernformations.com', None, 'http://www.bobbyhendrixpittsburgh.com', 'https://www.walmart.ca/en/stores-near-me/westbrook-store-3009', None, None, 'http://www.quinceflowers.com', 'http://storelocator.staples.ca/stores/en_CA/AB/Calgary/132', 'http://paintingwithatwist.com/pittsburgh-west/', 'http://www.mitierravegas.com', '1592511053', 'http://hairuntangled.com', '1592511060', 'http://www.modcom.ca', None, None, None, None, 'http://www.lepiratedelaval.ca', 'http://www.fitzflooring.com', 'http://www.verizonwireless.com/stores/north-carolina/charlotte/pineville-308497/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://Www.alabonlibonc.com', 'https://www.samedaymmjcards.com', 'http://www.gametruckparty.com/charlotte', 'http://www.phoenixrealestatephotography.com', 'http://www.jeffwokutch.com', None, 'http://www.ampm.com', 'http://www.advancedgrafixonline.com/', 'http://fasttech.ca', None, 'http://www.nightlifetourslasvegas.com', 'http://www.thesweetspotconcord.com/', 'https://bishops.co/locations/santan-village/', 'http://www.youngbloodhaircutters.com', 'https://ad.doubleclick.net/ddm/clk/318369417;146857521;q?https://www.safelite.com/stores/Gastonia-Mobile-Auto-Glass?utm_source=yelp&utm_medium=list&utm_campaign=Addressblock&utm_content=28052_NC', None, None, 'http://www.cakefrenzy.com', None, 'http://dvuexperttailor.com', None, 'http://chase.com', 'http://www.agincourthyundai.com', 'http://www.visartvideo.net/', 'http://wruw.org/', 'http://www.alluredermatology.com', '1592511163', 'https://summerlin.wini.com', None, 'http://www.nextlevelprodjs.com', None, 'http://www.bettyloucruises.com', None, 'https://www.vistapaint.com/stores/48', 'http://www.trenzlasvegas.com', None, 'http://matmb50.wix.com/aeglv', '1592511190', 'http://www.venetian.com/', 'http://www.goautosalesaz.com', 'https://www.toyotatechscharlotte.com', '1592511201', 'http://www.cantinalaredo.com/', None, None, 'http://www.bankofthewest.com', None, 'http://www.clairhurstpediatrics.ca/', 'http://www.citronsound.com/', None, 'http://www.michaelkors.com', 'http://www.sunprint-cafe.com/', None, 'http://amatospizzaetna.com', 'http://www.oakesonpt.com', None, 'https://www.freewayinsurance.com/office-locator/freeway-insurance-phoenix-az-85028/', 'http://www.kineticoaz.com', 'http://www.mcmichael.com', 'http://www.joetint.com', 'http://paradisevalleyseptic.com', 'http://www.harvestcaferestaurant.com', '1592511253', None, 'http://www.arentwenaughty.com/', 'http://www.momohairbyliz.com', 'http://bumperdoctoratlanta.com/', None, 'http://www.9thislandsup.com', 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', '1592511274', None, None, 'http://cruxcomptoir.com', 'http://arcohandcarwash.com', None, 'http://www.bgood.com', None, 'http://www.urbandental.ca/', None, 'http://www.skinfixstudios.com', 'https://www.chick-fil-a.com/willoughbycommons', 'http://www.camelbackwomenshealth.com', None, None, 'https://www.bannerhealth.com/locations/gilbert/banner-urgent-care-2', 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://www.gilbertroaddental.com', 'https://megafurnitureusa.com', 'http://www.cipssportsbar.com', 'http://landscapearchitectslasvegas.com', 'http://Planetsub.com', 'http://www.bmd-media.com', 'http://v3tri.com', '1592511332', None, None, 'https://www.frysfood.com/storeHours?store=66000676', 'http://www.usawaterproofing.com', 'http://www.thewirelesscenter.com', 'http://www.kegsteakhouse.com/en/locations/QC/pointe_claire/pointe_claire_keg/', 'http://lalosmadison.com', 'https://www.lifetime.life/life-time-locations/nc-charlotte.html?utm_medium=directory&utm_source=yelp&utm_content=homepage', 'https://www.sunrisepreschools.com/locations/40th-st-ray/?utm_source=yelp&utm_campaign=online_listing_phoenix_271&utm_medium=referral&utm_term=business_url', 'http://www.palms.com?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.ivlvhydration.com', 'https://www.shopdevannalove.com', 'http://www.alansfilipinorestaurant.com', 'http://sewickleyhotel.com/', 'http://www.rjsautopros.com', 'http://www.4azsparepair.com/', 'http://www.gowireless.com/shop/en/gowireless', 'http://moderndentaleastvalley.com', '1592511387', 'http://www.searshardwarestores.com/locations/bainbridge-oh', 'http://www.themidpoint.ca', 'http://www.desertsmilesdental.com/', 'https://www.suncitygrand.com/golf/golf-course-information/granite-falls-south', 'http://wildeagle.com', 'http://www.statelinechryslerjeepdodge.net/', 'http://www.simon.com/mall/southpark/stores/nori-japan', None, 'http://www.kozetasalon.com', 'http://www.bathandbodyworks.com', 'http://www.gtdragon.com', 'https://locations.dennys.com/WI/MADISON/248083', 'http://www.longospizza.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FMSNWE', 'http://footesvalleyfarm.com/', None, None, 'http://www.handygalshome.com', 'https://elsupermarkets.com/phx-51st-5127-w-indian-school-rd/', 'http://www.zacfit.com', 'http://www.jomalone.com/', None, 'http://www.kitinteriorobjects.com/', 'http://www.sliwinplasticsurgery.com', 'http://www.protectingaz.com/', 'https://locator.chase.com/az/litchfield-park/5006-n-dysart-rd', None, 'http://www.PolcanMeatsCalgary.ca', 'https://www.wyndhamhotels.com/hotels/33338?tel=18885959874&iata=00093785&cid=fe:gn:20160201:yl:pp:gn:33338', 'http://www.allrocksupply.net', '1592511471', 'http://lasvegasmovingpros.com', 'http://luxurywatchbuyer.com', 'http://www.greengoddess.com', 'https://www.jaycoversthevalley.com/?cmpid=WJ0G_BLM_0006', None, 'http://www.shop380.com', 'http://www.harperhearingservices.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://cvdentalcare.com', 'http://rachelscoffeehouse.ca', None, 'http://www.accenteyes.com', 'http://www.nozzastudio.com', None, 'http://famousfamiglia.com', None, 'http://jaxmotorsportsaz.com', 'http://www.oldstationsubs.com', None, 'http://www.merrymaids.com', 'http://www.bulkbarn.ca/', 'http://www.thecurryleaf.com', None, 'http://zenhc.ca', 'https://briarhawk.com', None, 'http://www.arbys.com/', 'http://www.TheRoyalton.ca', 'http://nogrease.com', 'https://ad.doubleclick.net/ddm/clk/434335121;236814625;y', 'http://www.kovscekrenovation.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.europeanspecialtyfoodmart.com', 'http://www.simplecuremassageandskin.com', 'https://dutchbros.com/?utm_source=mesa&utm_medium=yelp&utm_campaign=website_mesa', None, None, None, None, 'http://www.acegiftsplus.ca', 'http://www.sacohair.com/', None, 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', 'http://hiltongardeninn3.hilton.com/en/hotels/quebec/hilton-garden-inn-montreal-centre-ville-YULCVGI/index.html?SEO_id=YELP-GI-YULCVGI', None, 'https://www.mrplumberphoenix.com', None, None, 'http://www.markhamsportsdome.com', 'http://madisonbootcamps.com', None, 'http://www.blackmountainpoolservice.com', 'http://www.newbalance.com', 'http://www.bedbathandbeyond.com', 'http://www.alphacommunitymanagement.com', 'http://www.bgood.com', '1592511669', 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://www.montrosenicolinnis.com/', 'https://craftbeermarket.ca/toronto', 'http://otgsportsgrill.com/', 'https://burgersnfriesforever.com', 'http://Northphoenixeyecare.com', 'http://www.spartanpharmacy.com', 'http://www.sakeroklv.com', 'http://www.paloverde.org/', None, 'http://www.riversidesportstherapy.com', 'http://www.pranacoffee.com', 'http://go.unlv.edu/maps/cox', 'http://www.starbucks.com/store/9298/', 'http://www.serenedentalaz.com', 'https://stores.joann.com/oh/elyria/2410/', 'http://www.picknpull.com/locations.aspx?ID=76&View=Detail', 'http://sushishop.com', None, None, 'http://www.aureastation.com', None, None, 'http://lemor.ca/', 'http://takeandbakemadison.com', None, None, 'https://www.t-mobile.com/store-locator/ca/concord/sunvalley-mall-2?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://vinum55.com/locations/#phoenix', 'https://www.liveatcyan.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', None, None, 'http://www.hausold.com', 'https://www.statefarm.com/agent/US/NV/Henderson/Eugene-Ramos-VSGXN1YS000?cmpid=JROR_BLM_0006', 'http://www.varsitybargrill.com', 'http://candrroofingaz.com', None, 'http://www.fireflycollectivephx.com', 'http://www.dairyqueen.com', None, None, None, 'https://simmonsgreenelaw.com', None, 'http://www.harrywinston.com', 'http://www.holtrenfrew.com/store/holt/stores/calgary', 'http://finishlinelv.com', 'http://www.fresh.com', None, None, '1592511849', None, 'http://www.carlscoolcars.com', 'http://www.crossfitculmination.com', 'http://www.daltoro.com', 'http://www.purdys.com/StoreLocationDetails.aspx?loc=199', 'http://www.microsoft.com', 'https://www.usps.com/', 'http://woodnhogbarbecue.com', None, 'http://www.mytaza.com/', 'http://scottmetzgersystems.com/', None, 'http://www.brookelynnbistro.com', '1592511895', 'http://www.starbucks.com/store/9298/', None, None, 'https://www.jiffylube.com/locations/az/phoenix/2098', 'http://www.tinahairstudio.ca', None, 'http://www.cpk.com/Location/Details/Southpark-Mall', None, 'http://www.alibabas.ca/index.php?route=common%2Flocation_details&loc_id=2', 'http://www.sportchalet.com', 'http://www.papajohns.com/', 'http://www.starbucks.com/store/9229/', 'http://thegroveto.com/', 'http://www.personalservicecoffee.ca/pages/markham#hours', None, 'http://www.mcginnis-sisters.com', None, None, 'http://www.wehaulohio.com', None, 'http://www.littlecaesars.com', 'http://datta-taxi-charter.business.site', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216494&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.poncecleaninglv.com', 'http://www.fountainhillsvet.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://locations.massageenvy.com/arizona/gilbert/2270-williams-field-rd.html', 'http://meritmoving.com', 'http://www.twogringostires.com', 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', None, 'https://www.moneytreeinc.com/branch/north-nellis', 'http://pristinecleancarpet.com', 'http://www.bedbathandbeyond.ca', 'http://www.floweraccents.ca//?srccode=yelp_track', None, 'http://www.alpinesporttherapy.com', 'http://www.donscarpetrestorationllc.com', 'https://stores.jcpenney.com/il/champaign/clothing-stores-champaign-il-2828.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2828', 'http://www.fotb416.com', 'https://www.smalv.com/OurCenters/HealthCareCenters/Eastern', None, 'http://veterantintingandblinds.com', 'http://www.skinnyduganslv.com', None, None, 'http://www.azhappytails.com', 'http://www.tntthenewtrend.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.taste-food.com', 'http://www.desertescapetan.com/', None, 'https://www.kumon.com/LAS-VEGAS-ALIANTE', None, 'http://fukuburger.squarespace.com', 'http://cashforgoldaz.com/', None, 'http://mdarepair.com', None, 'http://www.blackhills.plumbing', 'http://lacubana.ca', '1592512122', None, None, 'http://princetonclubxpress.net', None, 'http://www.olmstedlaserwash.com', 'http://www.radiantskinbyruth.com', 'http://www.dollarselfstorage.com', 'http://www.tsuki.ca', 'http://communitypharmacy.coop/', 'http://www.madisonturners.com/', 'http://petsittinghomesweethome.com', None, 'http://hideawaylv.com', '1592512164', None, 'https://www.finelineautogroup.net', 'http://www.shoelessjoes.ca/', None, None, 'http://www.foodbasics.ca', 'http://www.skiisandbiikes.ca', None, 'https://www.lawyersdui.com', 'http://restaurantfogo.com', 'http://www.telecityelectronics.ca/shop/', None, 'http://npiweb.com/mitchell', 'http://burritomasters.ca', None, 'http://www.donthecarcareman.com', 'http://www.dennys.com', 'http://www.chouskitchen.com', 'http://woodyslv.com', 'https://www.dashgrill.com/', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'https://www.mobilewheelrepaircompany.com', None, 'http://www.lasvegaspaininstitutes.com/services-avea-wellness-center-las-vegas.html', None, 'http://www.morningstarseniorliving.com/communities/assisted-living-phoenix-az-arcadia/', 'https://www.celestiashow.com', None, None, None, None, '1592512284', 'https://acrescannabis.com/las-vegas-nevada/', None, 'https://www.planetfitness.ca/gyms/mississauga-westdale-mall?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://loadedpierogi.ca', 'http://www.getdrivingtoday.com/', 'http://www.souvlakihut.com/etobicoke.html', None, None, 'https://www.elevateyogaaz.com', '1592512326', 'http://www.pioneersand.com', 'http://www.theretreatapartments.net', 'http://www.woodmans-food.com/sunprairie/', 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-saguaro?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-saguaro', 'http://tailoredinwhite.com', None, 'http://www.costaverdebbqchicken.com', 'http://Www.efsoundav.com', None, None, None, 'https://www.smartstyle.com/en-us/locations/nv/las-vegas/located-inside-walmart-3473-haircuts-3334.html', 'http://www.bissingrealestate.com', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.meineke.com', 'http://pitaland.ca/', 'http://www.bloorkiplinganimalclinic.ca/', None, None, 'http://provisioncoffee.com', 'http://www.smokinlingerie.com', None, None, 'http://arcanehairparlour.com', 'http://www.eltorito.com', 'http://www.acathospital.com', 'http://www.speedway.com', 'http://www.azdetailing.com', None, 'http://lasvegassportsperformance.com', 'https://www.carlosobriens.com', 'https://www.moonvalleynurseries.com', 'https://www.medicentres.com/chiropractic/', '1592514913', None, 'https://resveralife.com/locations/', 'http://www.konigould.com', 'https://local.biglots.com/oh/hartville/368?zcp=pd_local_yelp', 'http://www.wilcoxlegal.com', None, 'http://www.theperfectsaiztaco.com', 'https://www.greenvalleyranch.com/eat-and-drink/Tides/', None, 'http://www.traderjoes.com', 'http://www.fendi.com/', '1592514951', None, None, None, None, 'https://www.bestwestern.com/en_US/book/hotel-rooms.67029.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:67029', 'https://www.lovelightandhealingcenteraz.com', 'https://lernerandrowe.com/?utm_source=Yelp', 'http://coopertaxservice.com', None, 'http://www.vasetovase.com', 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', 'http://www.aycarambaeh.ca', 'http://www.midas.com/lasvegas/store.aspx?shopnum=1192&dmanum=480', 'https://fullypromoted.com/locations/phoenix-north-az/', None, 'https://www.hpb.com/072', 'http://www.easystreetautosales.com', None, 'http://socap.ca', None, 'http://Www.Reynoldstransfer.Com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXCC', 'http://www.paulhiltondds.com', None, 'http://www.7-eleven.com/?yelp=29384', None, 'http://www.afcsushi.com', 'https://www.torrid.com/store-details?StoreID=5256', 'http://www.chefthaiandsushiconcordnc.com', 'http://www.leiarizona.com', 'http://christmasinvegas.weebly.com', None, 'http://www.blackmarkettoronto.com', 'https://www.italgranitenorthroyalton.com', 'http://www.dunkindonuts.com', 'http://www.arizonamaternityclinic.com', None, 'http://www.lvscrap.com', 'http://www.banfield.com/veterinarians/az/phoenix/pho?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://stores.advanceautoparts.com/oh/solon/33313-aurora-road', 'http://www.spientertainment.com', None, 'http://www.krispykreme.com', 'https://www.kindercare.com/our-centers/charlotte/nc/086015?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=086015', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1386&s_cid=lsl0000001', 'http://sbeauty.business.site', 'https://www.bookdirtbusters.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZTD', 'http://www.roomconcepts.com', None, None, 'https://locations.massageenvy.com/arizona/chandler/2880-e-germann-rd.html', 'http://arizonacollege.edu', '1592515152', '1592515155', 'http://phosaigon.ca/', 'http://www.marcs.com/Stores/Marcs-Garfield-Grocery-Store-44125.aspx', 'http://www.teasehairparlor.com/', 'http://www.papayaking.com', 'http://www.addictedrealty.com', 'https://my.greatexpressions.com/appointments/reservations/168', None, 'http://www.atinama.com', None, 'http://www.sheppardwineworks.ca/', 'http://www.cottagechicstore.com', None, None, '1592515206', None, 'http://www.saunafin.com', 'https://www.moneytreeinc.com/branch/craig-road', None, 'https://www.radiantsmilesphoenix.com', 'http://Www.fusioncornerpizza.weebly.com', 'http://www.mycomputerworks.com', 'http://www.lyndeespetsitters.com', 'https://locations.levi.com/qc/mirabel/denim_mirabel_qc_ca112.html', None, 'http://www.azclinicalservices.com', None, 'http://www.vivoaz.com/', 'http://lvtreeservices.com', None, 'http://www.premiumvaporsinc.com', 'http://www.rainbowfootspa.net', None, 'https://www.solitudeatcentennial.com/?utm_medium=Listing&utm_source=Yelp', 'http://www.randallchiropracticandrehabilitation.com', 'http://www.gingerab.com', None, None, None, 'http://www.lincolnlodgeurbana.com', 'http://www.thekingsheadpub.ca', 'http://pinbaryyc.com', 'https://www.urbanbarn.com/en/stores-detail/?id=C203', 'http://www.smartandfinal.com', None, 'http://www.apartmentsphoenix.com', 'http://www.michaeltraylordds.com', '1592515290', 'http://robertostacoshop.com', '1592515296', None, 'https://stores.savers.com/az/scottsdale/savers-thrift-store-1178.html', 'https://www.mccormickranchgolf.com', None, 'https://local.fedex.com/ms/madison/office-1880/', 'https://www.boulevardurbanliving.com', 'http://www.partyprincess4adayaz.com', None, None, None, 'https://hathawayenvironmental.com', 'http://www.winninwindowtint.com', 'https://solexotica.com/169-church-st-toronto.php', None, 'http://kamakurajapaneserestaurant.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044280218096&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.colombiamia.ca/', 'http://brasseriebenelux.com/wellington', 'http://www.cellphone-repair.ca', '1592515344', None, None, 'http://spurcrosscycles.com/', 'http://eatdrinkblock.com', 'http://www.myazsearch.com', 'https://bananarepublic.gapcanada.ca', 'http://www.portofsubs.com', 'https://lasvegasliving.com/properties/viviani/', 'http://autocrossinc.com', None, 'http://www.softmoc.com', None, 'http://www.sincityrollerderby.org', 'http://www.bk.com', None, 'https://www.meineke.com/locations/az/peoria-1593/?utm_source=yelp&utm_medium=xvc', 'http://www.endlessideas.ca', 'http://www.samuraisams.net', 'http://www.computercentral.ca', 'http://www.iplumbnow.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.walmart.com/store/3465/glendale-az/whats-new', 'http://www.arbys.com', 'https://www.hyatt.com/en-US/hotel/canada/hyatt-regency-calgary/calrc', 'http://www.benefitcosmetics.com/?ext_id=yelp_ulta_010713_Yelp', 'http://www.andreadempseymd.com', '1592515420', 'http://greenthumblocal.com', 'http://www.hsroofing.com/', 'https://www.nanisgelato.com', 'http://www.coronadotrailsmaids.com', 'http://www.rvrentaloutlet.com/', 'http://www.dancesales.com', 'http://www.slickwaxbar.com', 'http://www.drgregsoffice.com/', 'http://chase.com', 'http://www.lifestylesbistro.ca', 'http://www.asiangrillonline.com', None, None, 'http://www.ihatecleaning.net/', None, 'https://3dbaby.us', None, 'http://bereadepot.com', 'http://www.rootsandtips.com', None, 'http://jacktherooferaz.com', 'http://www.gvstorage.com/self-storage/marine-rv-storage', None, 'https://www.wyndhamhotels.com/hotel/46880?tel=18003291073&iata=00093785&cid=fe:di:20161220:yl:pp:dius:46880', 'http://www.TheTomLoveGroup.com', 'https://bloor-fruit-market.business.site', 'http://HedleyOrtho.com', 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', None, None, None, 'http://www.starbucks.com/store/9334/', 'http://www.freedomdelivers.com/', 'http://www.champaignbarbershop.com', None, 'http://www.californiasalads.com', None, 'https://stores.guitarcenter.com/mesa?source=4GOA5AJBB', 'http://chandlerchamberofcommercetx.com', None, 'https://www.meijer.com/shop/en/store/133/?cmpid=OLA:040319:YelpGrocery', 'https://www.greatlakesbrewing.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', None, 'https://www.almostfamouspiercing.com/marketplace-mall', None, 'https://locations.postnet.com/az/cave-creek/29834-n.-cave-creek-rd', 'https://haircutmenhendersonnv.com', 'http://www.playatgila.com', 'https://www.littlesunshine.com/az-scottsdale/?utm_source=Yelp&utm_medium=yelp', None, '1592515548', 'http://edwardchavezkenpokarate.com', 'http://www.duckcommandermusical.com/', 'https://lvimed.com', 'http://www.ableappliances.ca', 'http://www.buddhafoodha.com', None, 'https://www.napaautopro.com/auto-repair/ontario/brampton-dixie-autopro/', 'http://www.dominos.com', 'http://www.foodlion.com', 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://hotdogheavenohio.com', None, 'http://blowoutdollhouse.com', 'https://stemsaflorist.com', None, 'http://www.mlewisphotography.com', 'http://www.janieandjack.com', 'http://www.eyecareprofessionalsaz.com/', None, None, 'http://store-locations.underarmour.com/nc/charlotte/UAFH-5524NFWS40?utm_source=yelp_website', '1592515607', None, 'http://radiantthaispa.com', None, 'http://www.clearbluenv.com', 'http://www.fiestafurnishings.com', 'http://www.shopangl.com', None, None, '1592515630', 'http://locations.lifelabs.com/details/ON/Newmarket/381/', None, 'http://www.pawn1st.com', 'http://www.revolutionhealthaz.com', None, None, 'http://www.lasvegas-furniture-repair.com', 'http://www.lataquizza.com/', 'http://www.holidayillumination.com/', None, 'http://www.vanlandinghamestate.com', 'http://www.lindtusa.com', '1592515661', None, 'http://www.oasistozen.com/stacey-hall/', 'http://byronbikes.com/', 'http://www.ucelomartialartsphoenix.com', '1592515676', 'http://www.HomeGuardAZ.com', 'http://www.GoodyHouse.com', 'https://www.archersbikes.com', None, 'http://www.akirasolon.com/', None, 'http://www.steelcitypetsitters.com', None, None, 'http://brimellcsn.com', None, 'https://advancehairandspacalgary.com', 'http://www.168markets.com/index-3-NV.html', 'http://www.hummusxpress.com/', 'http://www.stanleyphotography.ca', 'http://www.huttonville.com/alferriandsons/index.html', 'https://www.clevelandbiketours.com', 'http://www.ginnyswigs.com/home.html', 'https://www.thegoof.menu', 'http://www.rae-ann.net', None, None, 'http://www.latorrelaw.com', 'http://www.brownleejewelers.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://dealer.sprint.com/imobile', None, 'http://www.swirlscupcakes.ca', 'http://theopticalexpert.com', 'http://www.BlueDragonVaporShop.com', 'http://www.goodwill.vegas/thrift-store-68-4580-west-sahara-avenue-las-vegas-nv-89102/', 'http://www.duckee.ca', None, None, None, None, 'http://tokyodiscountvegas.com', 'http://www.canadiantire.ca/en/store-details/on/toronto-main-danforth-on.store.html', None, 'http://www.travisbeachumsalon.com', None, 'http://www.popboxmrkt.com', '1592515793', 'http://school.paulmitchell.edu/las-vegas-nv', 'http://www.ediblearrangements.com', None, 'https://siemslasik.com', None, 'http://untamedpet.com', 'http://www.tileshop.com/', 'http://marshmanagement.net', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, '1592515823', None, 'http://www.heritageaptsaz.com', 'http://www.musketeersgrill.com', 'https://www.tacodelmar.com', 'http://www.adogslifephoto.com/', 'http://www.IntegrativeAcu.com', None, '1592515845', 'http://www.culvers.com/restaurants/stoughton', 'http://www.devorehardware.com/', 'http://www.kammscornerab.com', 'https://www.kwiktrip.com/Locations/Details/766/', 'http://www.nauticalmind.com', 'http://samsxpresscarwash.com/matthews/', 'http://www.shortmanbrowns.com/', 'http://autobody.tgknd.com/', 'http://www.jackssonstrailers.com', 'http://www.cathedralbuffet.com/', 'http://www.ubreakifix.com/locations/phoenix', 'https://locations.waxcenter.com/az/goodyear/goodyear-0251.html', None, 'http://www.ultimatelashandbrow.com', '1592515884', None, 'http://www.summithumane.org', None, 'http://www.sassisalonscottsdale.com', 'http://sweetolenkas.ca', 'https://www.cavecreekcrow.com', 'http://Www.victoriasbrowsandbeauty.com', '1592515904', None, 'http://www.fatburgercanada.com', None, None, 'http://www.ymcacharlotte.org', 'http://www.myfoodcity.com', 'http://www.thatplace.org', 'http://garagedoorrepairlv.com', 'https://www.starbucks.ca', 'https://premieremoisson.com/fr/succursales/kirkland', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___phoenix', 'http://www.dance4less.com', 'https://www.myfavethai.com', 'http://miravita.com', 'https://www.familydentistpittsburgh.com', 'https://locations.dignityhealth.org/emergency-room-at-arizona-general-hospital-surprise?utm_source=LocalSearch&utm_medium=Facility&utm_campaign=Arizona&utm_term=EmergencyRoomatArizonaGeneralHospitalSurprise', 'http://www.clorebeauty.com/', None, 'http://www.bethelparkanimalclinic.com', None, 'http://www.achillesrunningshop.com', 'http://www.billdoratykia.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'https://stores.joann.com/wi/madison/319/', None, 'http://www.autorepairpeoriaaz.com', 'http://www.livewellbodyworx.com', None, 'http://www.scottsdalebible.com/northridge', 'https://www.brushandfloss.com/charlotte/', 'http://www.erinmillsmitsubishi.ca', 'http://www.connectionsarizona.com', None, 'http://www.rebuildingchampions.com', 'http://www.grandviewsteakhouse.com', None, 'http://www.wilkinslearningcenter.com', 'http://www.marriott.com/LASCY', 'http://search.grainger.uiuc.edu/top/', None, 'http://artsysmartsyclass.com', None, None, 'http://ajsautowhs.com', 'https://www.vinovolo.com/locations/Pittsburgh-PA', 'http://clickserve.dartsearch.net/link/click?lid=43700044282947950&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.jwlasvegasresort.com/JW-Marriott-Las-Vegas-Resort-Spa/Contact-Us-37.html', 'http://www.saharapgh.com', 'http://www.booktheride.com', None, 'http://www.cherryblossom-az.com', None, None, 'http://ahipoki.com', None, '1592516041', '1592516045', None, 'http://oandpcareaz.com', 'http://www.thedesertrose.com/', 'https://www.walmart.com/store/2050/henderson-nv/whats-new', None, None, 'http://www.hangerclinic.com/locations/Pages/Glendale.aspx', None, 'http://www.substationii.com', 'http://www.dollarama.com', 'http://sunchaselv.com/', 'https://www.theboulevardloungepgh.com', 'http://www.madisongreenhousestore.com', 'http://autotechps.com', None, None, 'http://www.lokahi.vegas', 'http://www.gogokaraokelv.com', 'https://www.ohiomobilegaming.com/order-now-3/', 'http://locations.harristeeter.com/sc/fort-mill/82/', 'http://www.sparkleautobody.com', None, None, 'http://www.elements-salonandspa.com', None, None, '1592516138', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3550+S+Rainbow+Blvd-Las+Vegas-NV-89103/storeid=16291', None, None, 'http://www.bwalker.biz?cmpid=MJ92_BLM_0006', 'http://www.ACEBakery.com', 'http://www.bigpaulsbbq.com/', 'http://www.ae.com', 'http://Www.coruscate-salon.com', 'http://laspalmasaz.com', 'http://www.orkincanada.ca', 'https://www.southbeachvegasapartments.com', 'https://asainbistrousa.business.site', 'http://www.thegaragedoorkingsaz.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sieverssecurity.com', None, None, 'http://www.lampcafeaz.com', 'https://locations.theupsstore.com/nv/north-las-vegas/5575-simmons-st?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.azlunchexpress.com/', 'https://collegehunkshaulingjunk.com?utm_source=yelp&utm_medium=organic', None, 'https://www.madcityoutdoor.com', 'https://www.walgreens.com/locator/walgreens-1725+northport+dr-madison-wi-53704/id=2967', 'http://cambridgesuitestoronto.com', 'http://www.bellajinhair.com', 'https://www.keffermazda.com', None, 'http://www.studiosalon.biz', None, 'http://www.theeyeglassfactory.com/', 'http://99only.com/store/Phoenix---12th-St./', None, None, None, 'https://chocolateshops.sees.com/oh/beachwood/chocolate_shops_beachwood_oh_oh-16.html', 'http://www.panelo.ca', 'http://www.lululemon.com/scottsdale/scottsdaleshowroom', None, 'https://www.cloudofgoods.com/las-vegas-nv', 'http://www.minicalgary.ca', 'http://lolcalgary.ca', None, None, 'http://www.whatabagel.com/index.php', None, None, 'http://www.allprohomeinspections.com', None, 'https://slimminghydrotherapylv.com', None, 'http://www.capsulemusic.com', 'http://lasvegasimplantdentists.com', 'http://www.thecal.com/vegas-hotel-reservations?disid=wmm_yelp_ca_corporate_californiacasino_organiclink', None, 'http://harvestkitchen.ca/', None, None, 'https://www.ohiomarijuanacard.com/cleveland-marijuana-doctor', 'https://www.patiomistingsystempro.com', 'http://bethanymontecalvo.com/Home_Page.html', 'http://www.crosscountryinspections.com', 'http://www.hugthairestaurant.com', 'http://greenfield-dry-cleaners.business.site', 'http://www.centralonline.tv/northeast', None, 'http://Hybirdautocleaningservice.ca', 'http://www.francisandsonscarwash.com/category/7878/francis-and-sons-car-wash-of-phoenix-az.htm', None, 'http://www.teavana.com', 'http://www.brazasportugal.com', 'http://www.nicksfurniture.com', 'http://tabernamexicana.com', 'http://www.LoveBoxAZ.com', 'https://www.moxieservices.com/locations/las-vegas/?utm_source=yelp&utm_medium=cpc&utm_campaign=2019_cpc', 'http://www.boardwalkfries.com/calgary-westsprings', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.cbdoulaservices.com', 'http://www.dunkindonuts.com', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592516417', 'https://www.speedycash.com/find-a-store/arizona/mesa/main-and-alma-school?utm_source=yelpstorelocator&utm_medium=Affiliate&utm_content=afflink', 'https://www.caesars.com/ballys-las-vegas/things-to-do/the-salon-at-ballys#.WQMTKFWGNQI', 'http://www.pizzaromarest.com', 'https://www.dr-akers.com', None, '1592516437', None, 'http://www.maplegrovedentalmadison.com', 'http://www.robertocavalli.com', 'http://www.peachykeenpets.com', 'http://thelotatedgewater.com', 'http://www.azcpr.com', 'https://www.ediblearrangements.com/fruit-arrangements?utm_campaign=StoreID336&utm_medium=Listing&utm_source=Yelp', None, None, 'http://www.7-eleven.com/?yelp=29384', 'https://www.rubios.com', 'https://www.swatch.com/en_us/store-locator/united-states/nevada/las-vegas/fashion-show-mall', None, "http://www.cdecard.com/PA%20Businesses/Chubby's%20Pizza%20and%20Hoagies/SPECIALS%20Chubbys%20Pizza%20&%20Hoagies.htm", 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', 'http://www.mrlube.com/en/mr-lube-near-you/Locate-a-Mr-Lube/oakville-345-speers-road.aspx?storeid=50&postalcode=L6K%203S5', None, 'http://www.eastofchicago.com', 'http://www.lastingkeepsakes.com', 'https://www.wellnesspittsburghpa.com', 'https://www.longsautomotiverepair.com', 'http://www.regenerateme.com', 'https://publicstoragecanada.com/self-storage-scarborough/28-estate-drive/', None, 'http://www.zikwid.com', 'http://www.muddyyorktours.com/', 'http://www.songskitchen.ca', 'https://www.englishdermatology.com', 'https://www.sportchek.ca/stores/stephen-avenue.html', None, 'http://www.h2-pure.com', None, 'https://keylimephoto.com', '1592516556', None, None, 'http://www.mstudiolasvegas.com', 'http://www.zimbrickbuickwest.com/?cs:pro=repman&cs:e=yelp', None, 'https://www.sleepcountry.ca', 'http://legalsolutionsnv.com', None, 'http://www.fritouchicken-pizzaforestlawn.com', 'http://www.longboardliving.ca', None, '1592516593', 'http://elitebridalshop.com', 'http://www.starbucks.com', None, 'http://www.sunnysidegrill.com', None, 'http://garage-doors-phoenix.com', 'https://rainsskinprescription.com', None, 'http://www.kivasbagels.ca/', None, '1592516639', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.livesomerset.com', 'http://www.ruiterconstruction.com', None, 'http://www.execucar.com/OurLocations/LosAngelesCALAX.aspx', None, None, 'http://tuttopastastatestreetmadison.mypub.website', '1592516673', 'http://www.cappyscage.com/', None, None, 'https://www.regencytowerslasvegas.com', 'http://www.liuyishouna.com', None, 'http://www.gemplers.com', 'http://www.smoothieking.com', 'http://www.fitrepublic.ca', 'http://www.terracesatnorthridge.com', None, None, None, 'http://thekennelklub.net', 'http://hiltongardeninn3.hilton.com/en/hotels/ontario/hilton-garden-inn-toronto-downtown-YYZDTGI/index.html?SEO_id=YELP-GI-YYZDTGI', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.approvedautoaz.com', 'https://www.rothconstruction.com', None, 'http://mecarealty.com/', 'http://www.cityartroom.com', None, 'https://www.flashandhound.com', None, None, '1592516766', 'http://www.vegasflowers.biz', 'https://www.allenedmonds.com/on/demandware.store/Sites-allenedmonds-Site/default/Stores-Details?StoreID=AE086-C', 'http://www.calalilycafe.com', None, 'https://www.brigadebarbershop.com', 'http://www.gabiswigs.com', 'http://www.fcfs.net', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006430791762&ds_s_kwgid=58700000444978102&ds_url_v=2', 'https://www.goettl.com/lasvegas/', 'http://www.mynewfoamroof.com/', 'http://www.agpvegas.com', 'https://www.walmart.com/store/2316/north-olmsted-oh/whats-new', 'http://www.myindiecoffee.com', 'http://www.mark-taylor.com/arizona/azul-at-spectrum/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', None, 'http://www.holytrinitypgh.org/festival', 'http://sharpvan.com/', 'https://fusionsushirestaurant.com', 'https://www.shepherdeye.com/locations/las-vegas/', 'http://www.playitagainsportsmesa.com', 'http://www.dignityrepairs.com', 'http://www.reflectionspoolandspallc.com', 'http://www.pvinteriorsaz.com', 'http://www.walmart.ca/en/walmart-stouffville-supercentre/1029', 'http://www.noordento.com/phone/index.html', 'http://www.banksdental.com', 'https://elpatiochampaign.com', 'http://www.satisfiedfrog.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.denhamandco.com', None, 'https://www.homebridge.com/branch/sewickley/', 'http://www.lbclosets.com', None, 'http://www.firstbank.com', None, 'http://www.dentureworldnc.com', 'http://www.banfield.com/veterinarians/az/phoenix/sah?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, None, 'https://locations.massageenvy.com/arizona/phoenix/7000-e-mayo-blvd.html', 'https://trapped.ca/locations/toronto.html', 'http://www.chatters.ca', 'http://www.benitashousecleaning.com', 'http://www.rjhardscaping.com', 'http://www.visualeyesoptical.ca', 'https://dapper-dons-barbershop.business.site', None, None, 'http://www.cransonupholstery.com', 'http://jjsmobilegrooming.com', 'http://www.desertsound.com', None, 'https://www.vaporizerstoremedina.com', 'http://www.lakefrontlines.com', 'http://www.mdofpc.com', 'http://empire-barbershop-llc.business.site', 'http://thebrunswickpump.com/', 'http://www.scorpionspecialists.com/', None, 'http://www.sunbeltelectricnv.com', 'http://www.biteyourtongueqc.com', 'http://www.molisanabakery.ca/index.html', None, None, None, 'http://lunabeautyspa.com', None, None, 'http://www.discount-drugmart.com', 'http://www.trapezelasvegas.com/', 'http://hatsoffhairdesign.net', None, None, 'http://www.affordableautoshippers.com', None, None, 'https://www.storage-solutions.org/storage/arizona/storage-units-avondale/13075-W-Indian-School-Road-139', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006430626690&ds_s_kwgid=58700000443428972&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.northcoastvape.com', 'http://www.mahlesrestaurant.com', 'http://www.mcdowellsonoran.org/trailhead/displayLocation/8#sthash.V5oIezTR.dpbs', 'http://northbarkpetsalon.com', 'http://www.dontbebroke.com/?utm_source=Yelp&utm_medium=Location%2BPage&utm_campaign=Yelp', None, None, 'http://www.getbangedsalon.com/', 'https://www.chantillystearoom.com', 'http://www.reviveit.store', 'http://luckysamuraigastonia.com', 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, 'http://www.pittsburghpa.gov/police', None, None, 'http://www.tirerimshop.com', 'http://promedhealthnc.com/', 'http://www.pizzapatron.com/', 'http://www.brugospizza.net/index.html', 'http://www.cowboyfoodanddrink.com', None, None, 'http://clevelandheightspetsitter.com', 'http://www.spadoctorlv.com/', 'http://mclaughlindistillery.com', None, 'http://locator.carolinas.aaa.com/locations/albemarle-road/', 'http://www.magnumyork.com', None, None, 'http://www.spartanbowl.com/', 'http://www.walkerplumbingaz.com', 'http://www.familydollar.com', None, 'http://www.alexanderssteak.com', 'http://www.americanwesthomes.com/', 'http://www.beautyguruceiba.com', 'https://www.SoldByTeddy.com', None, 'http://lasvegastransmissionshop.com/', 'https://www.americasbest.com/store-list/surprise-az-85379/', 'https://www.jugojuice.com', 'http://www.tempeschools.org/fees', 'http://www.stonebrookdrivingrange.com/#!restaurant/c8k2', 'https://www.t-mobile.com/store-locator/az/peoria/67th-peoria?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.panaderialaestrellalv.com', None, 'https://www.liveatcortesian.com', 'http://www.cabosmexicanrestaurant.com/', 'http://www.kingwaterfiltration.com', 'https://www.phoenix.gov/parkssite/Pages/Piestewa-Peak-Dreamy-Draw-Trails.aspx', None, 'http://www.nexdoorrealty.com/', 'http://www.papajohns.com', None, 'http://chartwellvet.com/', 'http://www.kaiseki.ca/', None, 'https://www.hkmeals.com', None, 'https://www.omnihotels.com/hotels/charlotte/dining/coin-bar', 'https://hotheadburritos.com/strongsville-oh', '1592573666', 'http://www.timhortons.com', None, 'http://www.coppas.com', 'http://www.theperfectionist.net', 'http://ucanada.com', 'http://zahands.com', 'https://verona.securityproperties.com', None, None, 'http://www.sundialaz.com', 'http://landscapingservicemesa.com', None, None, 'https://locations.mrtire.com/nc/gastonia/335-west-franklin-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://www.sundancevillageapts.com', 'http://www.silverstatecu.com', 'http://www.gandermountain.com/store-locator/details/De%20Forest-WI-113', 'http://a-1sprinklers.com/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.bandboxdogsalon.ca/en/', None, 'https://abbottpest.com', None, '1592573720', 'http://www3.hilton.com/en/hotels/arizona/hilton-scottsdale-resort-and-villas-SCTSHHF/index.html?SEO_id=YELP-HI-SCTSHHF', 'http://www.purecontract.com', 'http://www.rossstores.com', 'https://agents.allstate.com/regan-wood-las-vegas-nv.html', 'https://www.bannerhealth.com/locations/mesa/banner-desert-surgery-center', 'http://www.animalkindnessvet.net/', None, 'http://www.pier54az.com', None, None, 'http://www.azopt.net', 'http://www.icleangreenlv.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLELY', 'http://www.lampsplus.com/?sourceid=SMYELPTXLKStore16&cm_mmc=YELP-SM-_-Text-_-Link-_-Store16', '1592573752', 'http://www.headpaininstitute.com', None, None, None, None, 'https://www.mattressfirm.com/stores/az/scottsdale/mattress-stores-scottsdale-az-85260-6701.html', 'http://www.bi-lo.com', 'https://frankies.com/charlotte/', 'http://www.gocasamia.com', 'https://locator.chase.com/az/chandler/1155-s-arizona-ave?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.rotorooter.com', None, 'http://www.flooringamericachampaign.com', None, None, None, 'http://www.brothersitalianbistro.com', 'https://mymeatballplace.com', None, 'http://www.tobyssupperclub.com', 'http://www.termehcalgary.ca', 'http://www.blue-hem.com', None, 'https://stores.advanceautoparts.com/pa/west-homestead/437-west-7th-ave', 'https://www.csn.edu/locations/north-las-vegas-campus', 'http://www.roadreadyinspections.com', 'https://www.naturalgrocers.com/store/north-las-vegas', 'http://www.truburgerco.com', None, None, None, None, None, 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?language=en&STORE=11', 'http://www.mcdonalds.ca', 'http://www.fatburger.com', '1592573839', 'http://cleaning-fairies-calgary.com', None, None, None, 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://theblocknorthway.com', 'http://www.lastchancetattoolv.com', None, None, 'https://kairalitaste.ca', None, 'http://www.ouchclinic.com', 'https://www.proeyecenter.com', 'http://www.simplyskinlasvegas.com/book', 'http://www.woodingtonlake.com', 'https://www.philcron.com', None, 'https://in-perfetto.com', 'https://www.halendas.com/halendas-locations/mississauga/', 'http://kanjitoronto.com/#!/splash_page', 'http://rabbitrabbitteato.com', 'http://www.tungtungdanquenking.com', 'https://www.tidedrycleanersaz.com/locations/e-frank-lloyd-wright-blvd', None, None, None, 'http://www.bellasbrides.ca/', 'http://sunshine-irrigation.com', 'http://www.gotransit.com', None, 'http://primepestco.com', 'https://gladiator-burger-steak.business.site', '1592573921', None, 'http://drsweeten.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://lotusnailsbarnspa.com', 'https://www.lucisgrove.com', 'http://www.nogamblelv.com/', None, 'http://www.pegasuspoolandspa.com', None, 'https://www.eatmiramira.com', 'http://yourbestdrivingschool.com', 'http://www.fengfitfoods.com', 'http://www.bdtattoo.com', 'http://www.carsrelo.com', 'http://www.paysannegelato.com/', 'http://www.greyeagleresortandcasino.ca', 'http://creativesmileschampaign.com', None, 'http://www.esco4u.com', None, None, None, 'http://www.pghhealthandhealing.com/', 'http://www.resnicksgrocery.com/', 'http://www.snappyautospa.com', 'http://pompomrouge.com', '1592573990', 'http://www.celebritytuxandtails.com', 'https://www.aireserv.com/las-vegas', 'https://www.chamsine.org', 'http://www.sushilegend.com', 'http://www.gamestop.com', None, 'http://newdlebar-kent.com', None, None, 'http://southernsaladsandsandwichcompany.com/', 'http://www.mrsfields.ca', 'http://www.dunkindonuts.com', None, 'http://www.allamericanbarberacademy.com/', 'https://learninghowtoheal.com/contact-us/', 'https://www.aritzia.com/en/store?StoreID=1303', 'http://www.streetspicefoodtruck.com', 'http://www.nogielectric.com', None, None, 'https://zoeskitchen.com/locations/store/az/arrowhead', 'http://dynamiceyecare.com', 'http://www.cycleworldsuperstore.com/', 'http://www.corechiroaz.com', 'http://zeldensdelianddesserts.com', 'http://www.utm.utoronto.ca/', '1592574052', 'http://www.shell.us', None, None, 'http://www.visionquestbooks.com', 'http://www.mrhero.com', 'http://ballantynerocks.com', '1592574069', 'http://www.gilberthouserestaurant.com', 'http://qccatering.com/', 'https://www.haircutmenhuntersvillenc.com', 'http://www.littlestprince.com', 'http://paintlv.com/', 'http://www.yogaspace.net/home', 'http://www.mandalaybay.com/features-and-shopping/weddings/', None, 'http://www.worldfinecars.com', 'http://www.jjmadisons.com', 'http://www.allmountaincyclery.com', 'http://www.bigfellasbarbershop.net', None, 'http://www.pfdepot.com', 'http://www.royaltyautorepair.com', 'http://www.cbc.ca', 'http://www.icpolaris.com', 'http://www.zgallerie.com', 'http://www.foxchapelskiandboard.com', 'https://www.cfshops.com/fairview-mall.html', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'http://www.warehouseorganics.ca', 'http://www.springvalleypharmacylasvegas.com', 'http://wildfishaquarium.ca', None, '1592574135', 'http://www.julietteetchocolat.com', '1592574140', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://arahova-souvlaki.ca', None, 'https://dutchbros.com/?utm_source=chandler&utm_medium=yelp&utm_campaign=website_chandler', 'https://www.mynycb.com', None, 'http://www.einsteinbros.com/', 'http://www.grandbizarre.com', 'http://www.teavana.com/', 'http://www.martinautomuseum.com', None, 'http://jackastors.com/location-map/12/', 'http://www.waterfrontbikerental.com', None, None, None, None, None, 'http://www.premierlandscapinglakewood.net', 'http://www.proboxportablestorage.com', 'http://childurology.com', 'https://www.applebees.com/en/restaurants-higley-az/4712-e-ray-rd-99039', None, 'http://sanctuaryclt.org', None, None, None, None, None, '1592574211', None, None, 'http://www.mercersrestaurant.com/Home.html', None, 'http://www.mykidzdentist.com', 'https://www.sweetwaterscafe.com/sc-indian-land-redstone/', '1592574228', None, None, 'http://oldsollumber.com', 'http://www.superstore.ca', 'https://www.cricketwireless.com', None, 'https://www.simon.com/mall/arizona-mills', None, 'http://www.siriuspetstyling.com', None, None, None, None, 'http://www.dllawaz.com', None, 'https://local.albertsons.com/az/gilbert/861-e-warner-rd.html', 'https://www.loblaws.ca/store-locator/Loblaws+-+St.+Clair+Ave+West/1212?storeId=1212', '1592574270', None, 'http://www.solescapehealingarts.com', 'http://www.truvapenv.com', 'https://www.chicaschicken.net', 'http://www.symmetrypetgrooming.com', 'http://www.clara-tea.com', 'http://dxdumpsters.com/', 'http://www.harthouse.ca', 'http://www.originalchickentender.com', None, 'http://www.denimandsmith.com', 'http://www.galleryofflowers.net/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.crownpointrestaurant.com', 'http://www.tavern24.com/?utm_content=gastoniacoxrd&utm_medium=listing&utm_source=yelp&utm_campaign=local', None, 'http://www.steinmart.com', 'http://mulqueensewing.com', 'http://www.bramgatevw.ca', 'http://www.polishbylynn.com', 'http://www.santisacred.com', 'http://www.marvelmasonry.com', None, 'https://womensfitnessclubs.com/promenade-mall/?utm_source=yelp&utm_medium=search&utm_campaign=yelpcampaign', '1592574336', 'http://www.springlaser.ca/', 'http://www.lucianospizzanorthhills.com/', 'http://www.smilebydesign.com', 'https://scottsdaleearnoseandthroat.com', None, 'http://www.allreptiles.ca', 'http://www.chickenlandbbq.ca/', '1592574357', None, '1592574364', None, '1592574371', 'http://perfectskincenter.com', None, None, None, 'http://mulqueen.com', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'https://www.redlobster.com/locations/list/pa/pittsburgh/6150-robinson-center-drive', 'http://www.autonationnissanchandler.com', 'http://www.trappedcle.com', None, 'https://www.sportchek.ca/stores/southtrail-crossing.html', 'http://www.massagebypage.com', None, 'http://www.globemeatsmarket.com', 'http://www.haagendazs.us/shops', 'http://borough.ca/', 'http://www.pastorrestaurant.com/', 'http://www.bankofamerica.com', 'https://www.balzacs.com/locations/market-street/', 'https://www.jacksonhewitt.com/Tax-Preparation-Services-Locations/AZ/Mesa/13423/', '1592574438', None, None, 'http://www.cedarcreekgrille.com/', None, 'http://www.pazzopittsburgh.com', 'http://www.flywithkula.com', 'https://www.redrobin.com', None, 'http://www.uptowncheapskate.com/northphoenix', 'http://www.wendys.com', 'https://www.bannerhealth.com/physician-directory/g/gelow-randy-s?fullname=Randy+Gelow', 'http://BrewYourOwnBrew.com', 'http://www.teavana.com/retail/united-states/pennsylvania/pittsburgh/ross-park-mall%2886%29', 'http://www.mecksheriff.com', 'http://www.miphosongvu.com', 'http://www.muji.com/ca/', 'http://nuhairstudio.ca', None, None, '1592574500', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.chezcora.com/', 'http://www.pelicanssnoballs.com/', 'https://www.maids.com/67/?utm_source=Yelp', 'http://bellastonecare.com', 'http://www.labelladellerose.com', 'http://kellyspas.com', 'http://www.babalooscubancafe.com', None, '1592574536', '1592574540', None, 'http://www.bestlaminate.com', 'http://lasvegas.carenow.com/location/ann-simmons', 'http://herbaltherapywraps.com/', None, None, 'http://pghfresh.com', 'https://www.ihg.com/holidayinnexpress/hotels/us/en/monroeville/pitmv/hoteldetail', 'http://www.downtoearthinspection.com/', 'http://www.shacklands.com', None, 'http://www.sbarro.com', None, 'http://www.placentalady.com/', 'http://www.saintapkar.com', None, 'http://middleton.lili.org', 'http://www.occasiorealty.com', 'http://www.spectrumkatie.com', None, None, 'http://www.phoenixraceway.com', 'http://www.avondalenissan.com', None, 'http://originalpancakehouse.com/', None, None, 'http://www.dunkindonuts.com', 'http://belowdeck.ca/', None, 'http://www.phxdent.com/', 'https://www.hungryhowies.com/store/hungry-howies-00643?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00643&utm_content=Website_Link', None, '1592574645', 'http://foxchapelrealty.com', 'http://www.audiuptown.ca', 'http://www.grabowhandtoshouldercenter.com', 'http://vivabenegourmet.com', 'http://www.fourpeakschiropractic.com', 'http://www.thefurfactor.ca', None, 'http://www.standardinsulatingcompany.com', None, 'http://www.beachwoodflowershop.com', None, 'http://rainbowintl.com/henderson-nv', 'http://www.fatbastardburrito.ca', 'https://www.arizonapainrelief.com/location/az/phoenix', 'https://eastoverdental.com', '1592574693', 'http://www.fluxandform.com', 'http://www.pattyandfranks.ca', 'http://www.macys.com', None, None, None, 'http://mughaircuts.com/location/chandler', 'http://www.robertcentre.ca', None, 'http://www.havesmokewilltravel.net/', None, None, 'http://www.lonestarsteakhouse.com/', None, 'http://www.ardorbistro.com', 'http://www.fallasstores.com', 'http://www.gilbertpoolservice.org/', '1592574759', 'http://www.kitchenfair.net', None, 'https://mortonhysonmd.com', 'https://ad.doubleclick.net/ddm/clk/459145529;262878939;h', 'http://www.apeacefulfarewell.com', '1592574782', 'http://burritodrive.com/', 'http://www.wgcsportingclays.com', 'http://masquespa.com/', 'http://www.kamhan.ca', 'http://www.abautomotiveaz.com', 'http://www.wandaswaffles.com', 'http://www.roostersmgc.com/salondetail/default.asp?salonid=13108', None, 'http://www.thecleanspin.com', '1592574817', None, None, 'http://www.sophysclinique.com', 'http://www.thestrathconahotel.com', '1592574833', 'http://indieweddingdj.com', None, 'http://www.desertridgesmiles.com/', None, 'http://cuyahogalibrary.org/', 'http://www.andreasenchiropractic.com/', None, None, None, 'http://www.jambajuice.com', None, 'http://www.mesagrandeculturalpark.org', 'http://www.vaughanchrysler.com/', 'https://vegasnailspa.com', None, 'https://rockndeli.com', 'https://www.naturalgrocers.com/store/henderson', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/5715+N+19th+Ave-Phoenix-AZ-85015/storeid=17418?cid=ps_ylp_2020', 'http://www.jimbosgoodtimes.com', None, '1592574902', 'http://www.corpuschristicatholicchurch.com', 'http://www.bostonpizza.com', 'http://recreationalconceptsinc.com', 'http://www.a1bedandbiscuit.com', 'http://www.azcms.com', None, 'http://bestmadeshoes.com', 'http://www.gnc.com', None, 'http://mesa.wbu.com', None, 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'http://www.carlyleonthelake.com', None, None, 'https://www.cccnevada.com/treatment-centers/central-valley/', 'http://www.timhortons.com/', None, 'http://www.hiveofmadison.com', 'https://www.restoamir.com', 'http://hundredacresmanor.com', 'http://www.carnegiemnh.org/', None, '1592574974', 'http://www.papamurphys.com', None, 'https://locations.wafflehouse.com/nc-charlotte-449', 'http://www.coconails-spa.com/', 'https://mdgaragedoorsservice.com', None, 'http://www.homegoods.com', 'http://www.tasteofmediterranean.ca/', 'http://www.woodslawaz.com', 'http://www.riverruncc.com', None, None, None, 'http://www.franksautobody.com/', 'https://www.guardianprotection.com/yelp/2219-2220.aspx?utm_source=profile&utm_medium=yelp&utm_campaign=2018&utm_content=cleveland', None, 'http://www.kingfisherseafood.net', 'http://www.avantiautospa.com', 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-mckellips?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-mckellips', 'http://www.bk.com', 'http://www.abetterparty.info', 'http://www.sporttruckrv.com', 'http://www.diamondcabaretlasvegas.com', 'https://toronto-notary-public.com', 'https://stavrosranchlands.com', None, 'https://www.usps.com/', None, 'http://www.shakermotorslv.com', None, None, 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.amandavictoriabeauty.com', '1592575091', None, 'https://www.vipbeautysalon.org/our-team/vip-charlotte/', 'http://www.expressfitness.ca/scarborough', None, '1592575104', None, None, None, None, 'http://www.calgaryparking.com', None, '1592575125', 'http://www.greatharvestcharlotte.com', 'http://scottsdalesalonaz.com/', '1592575137', None, None, None, 'http://www.karelinstudio.com', '1592575154', 'http://www.takaramadison.com', 'http://www.thehouseofhunan.com/medina', 'http://chevyshopinc.com/home.htm', 'http://www.lovechirocenter.com', 'http://www.JimmyJohns.com', None, 'http://www.mancavebarbers.ca', 'https://sycamoreattyvola.com', None, 'http://www.flamingodurangoselfstorage.com/', 'https://www.thejoint.com/arizona/mesa/red-mountain-48026', 'http://www.tintgta.ca', 'http://www.parassons.com/', None, 'http://www.trendybambini.com', 'http://sushipalace.ca', 'http://newdirectionspgh.com', None, 'http://www.wickerpark.ca', 'http://www.mintbistro.com/', 'http://www.peoriapines.com', None, 'http://studio247chagrinfalls.com', 'http://mistermoons.jimdo.com/', 'https://www.merchantstreetcle.com', 'http://www.bargainlandusa.com', 'http://cherryroadautomotive.com', 'http://www.villaserenahenderson.com', 'https://guidepo.st/exploreprosperity', 'http://www.roofingcontractorarizona.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'https://myrosatis.com/peoriaolive/', 'http://www.meoweewowee.com', 'http://www.mossmanbrotherspools.com', 'http://www.simplyhairtoronto.com', 'http://caffefrancesco.com/', None, 'http://twilightcaribbean.com', None, 'https://www.westvalleytitle.com', 'http://www.superstitionfarm.com/', 'http://cartridgeworldphx.com', None, 'https://www.costasorrento.ca', 'https://www.azchoicefa.com', None, 'http://www.atlasappliances.com', 'https://www.donbaschjewelers.com', 'http://www.internationalhotel.ca/dining-and-events-en.html', 'http://www.hairbydesignsalons.com', 'http://www.beardsmithandbarber.com', 'https://www.enercare.ca/locations/willowdale', 'https://bostonpizza.com/en/locations/crossiron-mills.html', 'http://www.mrkssofticecream.com/', 'http://www.blusolspa.com', 'http://hwy55.com', 'http://www.swades.ca', 'http://www.piepal.com', None, 'https://order.subway.com/Default.aspx', 'http://sarahchristinegraham.com', None, 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.centum.ca/tony_spanogreco', 'http://www.agaveeyecare.com', 'https://www.publicstorage.com/california/self-storage-concord-ca/94520-self-storage/149?pid=wyelp&CID=1245&CHID=AFL', 'http://www.hanger.com/', 'http://www.spayaz.com/locations/pittsburgh-penn-hills-pa/', 'http://www.discountfamily.ca/en/', 'https://www.ironcladtattoos.com', 'http://www.michaelkors.com/', 'http://www.huespa.ca/', 'http://www.geeksandclicks.com', 'http://www.crescent.edu', 'http://www.towing-toronto.ca/', 'https://www.dominos.com', 'http://AZTotalHome.Com', 'http://www.bignissani90.com', 'https://www.dominos.com', 'http://www.sushizonelv.com', None, 'http://www.bakesaletoronto.com', 'http://www.bouncyworldlv.com', 'http://www.bluecrossvetltd.com', 'https://www.abrazohealth.com/our-locations/abrazo-west-campus', 'http://www.timhortons.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'https://azcashngo.com', 'http://www.locksandlashessalon.com/', 'http://www.rockychoc.com/', 'http://www.crowntownsubs.com', 'http://www.tradesunlimited.com', 'http://www.nobletitle.com', 'http://www.greenshield.ca', None, None, 'https://www.mercedes-benz-durham.ca', None, 'http://www.lafronterafoodtrucks.com', '1592575521', None, 'http://mahalls20lanes.com/', 'http://www.walmart.com', None, None, None, None, None, 'http://hsaz001.marketing.homesmartagent.com/agents/mr533', None, 'https://calgary.worldhealth.ca/location/midnapore/', None, 'http://www.autorepairshop-az.com', None, None, 'http://www.mrsparksllc.com', 'http://www.parkshvac.com', None, None, 'https://carylmechanicals.com', 'http://thinique.com/phoenix/mcdowell-mountain-ranch/', 'https://www.westerndental.com/en-us/find-a-location/arizona/glendale/5929-w-peoria-ave', 'http://www.goday.ca', None, 'http://www.lustrerooftopbar.com', None, None, None, 'https://www.thelolaaz.com', 'http://www.GigisCupcakesUSA.com/', 'http://www.aerotek.com/locations/united-states/arizona/west-phoenix.aspx', 'http://www.meltingpointhotyoga.com', 'https://www.zipscarwash.com/location-detail/146', None, None, 'http://www.charmeck.org/', 'https://heroburgers.com/locations/yonge-weldrick/', None, None, 'http://www.bordermx.ca', 'https://www.choicehotels.com/pennsylvania/new-kensington/quality-inn-hotels/pa246/rates', 'https://redrock.sclv.com/Entertainment/Rocks-Lounge.aspx', 'http://www.performancerealtynv.com/', None, 'https://locations.timhortons.com/ca/on/stouffville/5534-main-st-west.html', None, 'https://locations.monro.com/pa/verona/60-allegheny-river-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.thelockdoctoraz.com', None, None, 'https://www.wyndhamhotels.com/hotel/03073?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:03073', None, None, 'http://www.zenskinnv.com', 'https://aztirepros.com', 'http://www.ccscafe.net', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://fitness4home.com/store-locator/phoenix-i-10-superstore/', 'http://www.nuluxlaserspainc.ca', None, 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', 'https://www.popeyes.com', None, 'http://www.fixitadvantage.com', None, 'http://www.bk.com', 'http://www.becksflooringaz.com/home.html', None, 'http://www.bellasolanoapartments.com/?campaign_code=yelp_Bella_Solano_AZ_85015', 'http://bostondentalgroup.com/locations/hola-dental/', 'http://www.donmasterscpa.com', 'http://www.inkdoodle.ca/About-Us.html', None, None, 'http://dunxcoffee.com', 'http://fusionhairstudio360.com', 'http://noire-et-blanche.ca/', None, 'http://bellenynails.com', None, None, 'http://www.annaslinens.com/?utm_source=Yelp&utm_medium=Annas_Homepage&utm_campaign=Yelp', 'http://www.deseretindustries.org', 'https://www.mrhero.com', 'http://nutmegbakeshop.com', 'http://www.cannerycasino.com/dining/vinos-ristorante', 'https://www.fetchpetcare.com/south-and-west-Pittsburgh/', 'http://www.hogtownvegan.com', None, None, None, 'http://www.dazzlingbistro.com', 'https://www.vivasalonlv.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.torrid.com/store-details/?StoreID=5022&CM_MMC=CSE-_-YLP-_-ORG-_-SITE', None, 'http://www.RobinsonRanch.org', 'http://alignpgh.com/', 'http://www.sheetz.com', 'http://www.ironcare.com', 'http://www.samuraicomics.com', 'http://gooddrivers.ca', 'http://www.megliospizza.net/', 'http://www.icetango.com', 'http://www.crepedelicious.com', 'http://congeedynasty.com/', None, 'http://nationaleventvenue.com/', 'http://www.portofsubs.com', 'http://allvegaspropertygroup.com', 'https://www.goldenlandrestaurant.com', 'https://www.batteriesplus.com/store-locator/tn/madison-rivergate/batteries-plus-552?utm_source=yelp&utm_medium=local&storecode=552', 'http://www.pghwaterlimo.com', 'http://www.ohara.pa.us/parks.asp#squaw', 'http://www.robertsonfamilychiro.com', 'https://www.aaautocarelv.com/locations/400-simmons-st/', 'https://www.softsurroundings.com', 'http://www.embracepetinsurance.com', None, 'http://lowes.com', 'https://www.artinstitutes.edu/las-vegas/about/opus-too-restaurant', 'https://www.associatedfinishes.com', 'http://allcustomiron.com', None, '1592575959', None, 'https://www.thepaincenter.com/?utm_source=yelp&utm_medium=referral&utm_content=arizona-arcadia', 'http://www.evansfursandleathers.com/', 'https://www.fashionflowerscharlotte.com', 'http://www.eastofchicago.com/', 'http://www.bodyheattanning.com', 'http://www.fairoaksnursery.net', 'http://www.peraltalawgroup.com', 'http://topdoggrooming.co', None, None, 'https://dutchbros.com/?utm_source=scottsdale-3&utm_medium=yelp&utm_campaign=website_scottsdale-3', None, 'http://Amanihairstudio.com', 'http://elitehoamanagement.com/', None, 'https://irrigationcomplete.wixsite.com/mysite-1', 'http://www.hurleyfamilyautoaz.com', None, 'https://www.wellsfargo.com', '1592576026', 'http://www.kelseys.ca/', None, None, 'http://www.norterradentistry.com', 'http://www.accentcomfortservices.com', None, None, 'http://llvsportsclub.com', '1592576064', 'http://www.uniqlo.com/ca/en/shop/cf_markville.html', 'http://timecentral.com', None, 'http://pierrelalande.com/', None, None, None, 'http://hobocampercountry.ca', 'http://www.certifiedtrees.com', 'http://www.shoppersdrugmart.ca', 'http://www.atouchofserenitymassage.com/', 'http://link.hertz.com/link.html?id=46215&LinkType=LEISURE&TargetType=Homepage', 'http://www.nuebrowstobrazilians.com', 'http://www.valleygaterefinishing.com', 'https://www.vanbuickgmc.com', 'https://www.advantagestorage.net/self-storage/az/avondale/advantage-storage-avondale/', None, 'http://mosmoscoffee.com/', None, None, 'http://www.veldarosemedical.com', None, 'https://tnlasvegas.com', None, 'http://www.bk.com', 'https://www.chilis.com', None, 'https://www.applebees.com/en/restaurants-charlotte-mi/1642-packard-hwy-84002', 'http://www.tacotacoaz.com', 'http://www.marriott.com/hotels/travel/cltts-towneplace-suites-charlotte-university-research-park', 'https://www.marks.com/en/stores/calgary-macleod-6636-macleod-trail-sw-chinook-station.html', 'https://www.marcs.com/stores/marc-s-north-olmsted-grocery-store-44070', None, 'https://stores.jcpenney.com/az/phoenix/clothing-stores-phoenix-az-1480.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-1480', 'http://salsautoworks.com', 'http://www.shenkeracademy.com', 'http://www.deansilvermd.com/', 'https://cocofreshtea.ca', 'http://a1sprinklerexperts.com', 'http://www.drpedja.com', 'http://www.thedetoxmarket.ca', None, 'http://popeyes.com', None, 'http://restaurants.quiznos.com/oh/brookpark/brookpark-44142', None, 'http://www.stroseanthem.com', 'http://www.cyclecorpsfitness.com', None, None, None, 'http://www.platosclosetmississauga.com', None, None, 'http://spadinavet.com', None, None, None, 'http://www.danishpastryhouse.ca', None, 'http://www.biltmoreclubliving.com', 'http://ricksbakeryurbana.com/', None, 'http://ursarestaurant.com', 'https://www.petesbigbite.ca', 'http://www.dinerdeluxe.com', 'http://www.gentledentalseville.com', 'http://www.mataharigrill.ca', 'https://mymothers.business.site', 'http://www.acpro.com/locations/las-vegas/', 'http://www.grilltime.ca/', 'http://www.thevisionyard.com', 'https://www.gorefreshdental.com/locations/refresh-dental-medina/', 'http://sunshinecleaninglv.com', None, 'http://www.arizonausedcars.com/', 'http://www.croatiancentre.ca', 'https://hibachixpressgrille.us', 'http://www.cleanjuice.com/Matthews', 'http://www.tristargasservices.com', '1592576332', 'http://www.phxgt.com', None, 'http://www.marriott.com/hotels/travel/yyzwy-residence-inn-whitby', None, 'http://sevalleyobgyn.com', None, 'http://www.tradingacademy.com/toronto/', None, 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'https://molinaris.com', 'https://www.wellsfargo.com', 'http://www.readypowersports.com', None, 'http://fundflowers.com', 'http://www.kimmberlycapone.com', 'http://www.lvjewelryexchange.com', 'http://voodoobikeworks.com/', 'http://www.metropolisohio.com', None, 'http://www.midcenturysalvage.com', 'https://www.yardhouse.com/locations/oh/westlake/westlake-crocker-park/8346?cmpid=br:yh_ag:ie_ch:dry_ca:YHQ121LOCURL_dt:20200609_sn:yelp_gt:westlake-oh-8346_pl:locurl_rd:1045', 'http://sugarthieves.com/', 'https://www.smartstyle.com/en-us/locations/on/markham/located-inside-walmart-1109-haircuts-5137.html', 'https://agents.farmers.com/nv/las-vegas/aaron-schnitz?SourceID=AMPALFYEAG&utm_medium=Local&utm_source=Yelp', None, 'https://stores.mattressfirm.com/nv/lasvegas/mattress-stores-las-vegas-nv-7075.html', 'https://pr.business/phoenix-hot-air-balloon-rides-aerogelic-ballooning-phoenix-arizona-2', 'http://www.northchurchtowers.com/', None, 'https://www.ediblearrangements.com/fruit-arrangements?utm_campaign=StoreID336&utm_medium=Listing&utm_source=Yelp', 'http://www.meatballz.net', None, 'http://www.airairair.com', 'https://www.kingbudz.com', None, 'http://www.dragonpearlbuffet.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282959626&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.tobinlawoffice.com/chandler-criminal-defense-lawyer', None, 'http://www.sleepmed.ca/', 'https://beerfests.com/events/real-wild-woody-beer-festival/', '1592576472', 'http://projectgigglewater.com', 'http://www.bookcity.ca', None, 'http://www.towerchrysler.com', 'http://www.lunchboxwax.com/salons/scottsdale', None, 'http://www.alicatspa.com', None, None, 'https://www.publicstorage.com/california/self-storage-glendale-ca/91204-self-storage/70?pid=wyelp&CID=1245&CHID=AFL', 'http://www.napolitanpizza.com', None, 'http://local.firestonecompleteautocare.com/north-carolina/charlotte/5340-e-independence-blvd/?lw_cmp=IYP_YPC_MLP_10790', None, 'http://www.delicieuxjuicebars.com', None, '1592576525', 'http://pittsburghantiqueshops.com', None, 'https://www.summerlyliving.com', 'http://browsbeautyink.com', 'http://www.fairmont.com/scottsdale/dining/bourbonsteak/?genid=yelp_scp_bourbon_yelp_enhanced&utm_source=yelp&utm_medium=paid_referrer&utm_content=scp_bourbon&utm_campaign=yelp_enhanced', None, None, None, None, 'http://www.grandavenuepizzacompany.com/', 'http://outlawbbqshack.com', None, 'https://www.computerdoctor-bg.com', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Phoenix/AZ/8160', 'https://centralaz.com/Gilbert', 'https://www.bebomia.com', 'http://scores.ca', 'http://www.jmmovers.net', None, 'http://www.mermaidstale.net', None, 'http://Pittsburgh.certapro.com/?source=Yelp', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.restaurantangkoria.com', 'http://dejavu.com/club-locations/deja-vu-adult-emporium-las-vegas', 'http://kimcourtneyswim.com', None, 'https://urbanthaiongerrard.com', 'http://www.lasvegashealthpoolservice.com', 'http://www.vietfooddelivery.com/', 'https://horsebacktrailriding.com', 'http://www.usairsolutions.com', 'http://www.trailthis.com', 'https://www.kumon.com/gilbert-southeast', 'http://www.urbanmuttslv.com', None, None, None, None, None, 'http://www.organicskincarebcnv.com', 'http://www.raacknroll.com', 'https://www.tacoelchapo.com', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/mississauga/yyzam/hoteldetail', None, 'http://www.fourpeaksdental.com/', 'https://www.associatedbank.com/location/WI/madison/2001-londonderry-dr', 'http://pulpjuiceandsmoothie.com', 'http://www.lovelessboutique.com', 'https://www.carstar.ca/en/locations/on/toronto/carstar-toronto-millwick-16035/', 'http://goodwillswpa.org/computer-store', 'http://www.liquid-planet.com', 'http://www.wingilariver.com/index.php/wild-horse-pass/dining/cas', None, 'http://www.bannerbuzz.ca', 'http://www.bullmooseguns.com', 'http://www.gallucciwinery.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.thedeckoneast.com/index.php', 'http://www.swansproperties.com', 'http://www.charlottenc.gov', 'http://www.prioritypetsitting.com', 'http://thericekitchen.com', None, 'http://pulpjuiceandsmoothie.com', 'https://www.bahamabreeze.com/locations/pa/pittsburgh/pittsburgh-robinson-township/3041?cmpid=br:bb_ag:ie_ch:dry_ca:BBQ121LOCURL_dt:20200615_sn:yelp_gt:pittsburgh-pa-3041_pl:locurl_rd:1021', 'http://lifeissweetpgh.com/', 'https://www.calgarycoop.com/stores/shawnessy/', 'http://celebritytanning.com', 'https://www.regmovies.com/theatres/regal-montrose-movies/0182?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Montrose+Movies', 'http://nailspa4u.com', 'http://www.2020mhi.com', None, 'http://www.thepuppystorelasvegas.com', 'http://oakvillemovers.net', 'http://www.inmotionservices.ca', None, None, None, None, 'http://www.eyestop.net/maps.html', None, None, 'http://bluedotpools.com', 'http://michaelasdancemagic.com', 'http://www.tforcefinalmile.com', None, 'http://www.clemetrobar.org', 'http://www.newagecosmeticsurgery.com', 'https://www.novelrio.com', 'http://www.elithehandyman.com', '1592576829', None, None, None, None, None, 'https://rentprogress.com/houses-for-rent-phoenix-az/', 'http://www.cactussports.com', 'http://www.maravillaapts.com', 'http://www.mrhandyonline.com', 'http://www.cineplex.com/Theatre/silvercity-newmarket-cinemas-xscape', None, 'http://socialappsinc.com', None, 'https://www.zenmassageusa.com/SouthPark/', 'http://www.celebrityvault.com', 'http://www.hunanbythefalls.com/', 'http://randpinstall.com', 'https://www.criminaldefenseoflasvegas.com', 'http://www.luxor.com/dining/dining_company.aspx', 'http://www.streetsofnewyork.com', 'https://www.usstoragecenters.com/self-storage/arizona/chandler/tower-storage/181', None, 'http://wisconsinvision.com', 'https://www.hennesseysalonspa.com/stores/hennessey-salon-spa-chinook-centre-calgary-ab-t2h-0k3-salon-5841/', 'http://www.hankstable.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.360physicaltherapy.com/locations/fountain-hills', 'http://www.oldemeckbrew.com/', None, '1592597495', 'http://www.theheartykitchen.ca', None, 'http://healthcareprep.edu', None, None, 'http://www.lizardville.net', None, 'http://www.cox.com', 'https://www.searshomeservices.com/locations/appliance-repair/wi-madison/43-east-towne-mallc', None, None, None, None, None, 'http://www.everettapt.com', 'http://www.funtasticforest.ca', 'http://tiredawgs.com/', 'https://www.swlasvegas.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=yelpCPC', None, None, 'http://www.pasqualebros.com', 'http://www.jansoncleaners.com', 'http://www.dunkindonuts.com', None, 'https://us-tire-center-auto-repair.business.site/?m=true', 'http://www.JimmyJohns.com', '1592597592', None, None, None, 'http://www.railwaybarbershop.com', 'http://www.tippytoes702.wix.com/tippytoes702', None, 'https://www.aqua-tots.com/peoria', None, 'http://www.nowfeelgood.com', None, 'http://www.hannasitalianice.com/', 'http://cinema.wisc.edu/', None, 'http://www.mandarinoriental.com/lasvegas/dining/', 'http://pitapit.ca', None, None, None, 'https://locations.jackinthebox.com/us/ca/glendale/1200-w-glenoaks-blvd', None, 'https://www.lulubar.ca', 'http://www.roadrunnerpoolservice.com/', None, 'http://www.haircrafterssalons.com/', None, 'http://ridenstylecustoms.com', '1592597670', None, None, 'http://www.epicerieloco.ca', 'http://www.thebodytherapycenter.com/', 'http://qdoba.com', 'http://storelocator.pepboys.com/pepboys/stores/henderson/henderson/00869', 'http://goodvibeztattoo.com', None, 'http://elcortezhotelcasino.com/dining/', 'http://www.thebattlegroundspa.com', 'http://www.sailpointeatlakenorman.com', 'http://www.djtommyfoose.com', None, 'http://www.shagitlikeyoumeanit.ca', None, 'https://spankyssmokeshopaz.com', None, 'http://www.everythingbutwater.com', 'http://www.elpatronmexicanrestaurant.com', 'https://www.nike.com/ca/retail/s/nike-factory-store-vaughan-mills', 'http://www.foxysalonsuites.com', 'http://www.pcofmesa.com', 'http://ertcpr.com', 'http://www.privatepleasures.ca', 'http://www.essen-haus.com/', 'http://www.lepapillonpark.com', None, 'http://www.dunkindonuts.com', None, 'http://www.kababgrill.ca', None, 'http://lasvegastrailriding.com/', 'https://www.chevronwithtechron.com', 'https://www.anytimefitness.com/gyms/2797/Mississauga-ON-L5R-3V2/?utm_source=yelp&utm_medium=local', 'http://www.jeresfreshstartsalon.com', 'http://www.benjerry.com/', None, 'http://wyliespub.ca/', 'http://cabanaonthomas.com/', 'https://wavescoffee.com/our-stores/springborough', None, 'http://www.blackandcoldcreamery.com', None, None, None, None, 'https://plumbingmedic.net', 'http://www.epoquesalon.com', None, 'http://www.arizonagrandresort.com/?utm_medium=enhanced-profile&utm_source=Yelp', None, 'http://www.gaetanosbanquetcenter.com', 'https://www.sweetdoughdonuts.com', 'http://www.ihg.com/holidayinn/hotels/us/en/cleveland/cleat/hoteldetail', None, 'http://www.sallybeauty.com', 'http://www.saffronkitchen.com', 'http://www.super8.com/hotels/hotel-overview?wid=ps:addppc_yelp&reg=appc-_-ylPROPP-_-07615-_-SUP&hotel_id=07615&cid=whg_s8_yelp', 'http://www.FirstClassReflexology.com', None, None, 'https://locations.timhortons.com/ca/on/richmond-hill/1070-major-mackenzie-dr.html', None, 'http://www.sweettoothpedo.com/', 'http://thebestlittlehairhouseinpittsburgh.com', 'https://busangalmaegibbq.com', None, 'https://www.frysfood.com/storeHours?store=66000129', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'http://www.terriblescasinos.com/', 'https://www.floydsbarbershop.com/glendale-arrowhead/', None, 'http://www.secondskinmedspa.com', 'https://www.originaljoes.ca', 'https://pizzapit.biz', 'http://sunvalleypets.org', None, 'http://whataface.com', None, None, 'http://www.adasfishfry.com', 'https://aclosetfullofdresses.com', None, '1592597875', None, None, 'http://www.lupitasmexicanrestaurant.info/index.html', None, 'https://zoltanwedding.photography', 'http://www.parama.ca', 'http://www.timhortons.com/', 'http://www.gocheckers.com', 'http://www.familydollar.com', '1592597903', 'http://www.iveyautobodyspecialist-il.com/', 'http://www.tru-air.com', None, None, 'http://www.greenwoodpah.ca', 'http://www.delatorreop.com', 'http://www.popeyeschicken.ca', 'http://www.speakeasytherapylv.org', 'https://bigeasydogdaze.com', None, 'http://www.portofsubs.com', None, 'http://www.melrosetvaz.com', 'http://www.themuscleclinicaz.com', None, 'http://www.vita-urbana.com', 'http://nevadapain.com', 'http://www.sandwichbox.ca', 'http://locations.arbys.com/us/pa/pittsburgh/4810-mcknight-rd.html', 'http://www.acherolasvegas.com', None, None, None, 'https://www.petittigardencenter.com', 'https://www.mattressfirm.com/stores/az/mesa/mattress-stores-mesa-az-85215-7026.html', 'http://www.velopops.com', 'http://www.yogisbarandgrill.ca', 'http://www.flossyshd.com', 'http://www.sugarsbakerylv.com', '1592597978', 'http://mekongplaza.com', 'http://www.lvsofafactory.com', 'http://www.suncitiesgaragedoor.com/', 'http://www.montanas.ca', None, 'http://glamstudiobyjoanna.com', 'http://originaldivaextensions.com/', 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'http://azmotomania.com', 'http://littlecaesars.com/', 'http://ifixappliances.ca', 'https://www.avenidadental.ca', None, None, None, 'http://www.ritassmcclintock.com', 'http://www.KohVideo.com', None, 'https://1001nightsrestaurantmesa.wordpress.com', 'http://www.haikugrill.net/', None, None, None, 'http://www.makeupfromchelsey.com', None, 'https://locations.sonicdrivein.com/ok/chandler/816-e.-first-street.html', 'http://bsbarbershop.com', None, 'http://www.gentledentaluniversitydrive.com/', '1592598056', None, 'https://360-visuals.com', 'http://www.drhirjieyecare.com', None, None, 'https://new-york-bagel-bakery.business.site', None, 'http://www.yorku.ca/', None, 'https://www.umcsn.com/Quick-Cares/Quick-Care-Locations-Enterprise.aspx?intMenuID=112&intPageID=190', 'http://www.swirlsaz.com', None, None, None, 'http://www.saltrivervet.com', 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', 'http://www.luxybarbers.com/', None, None, 'http://www.s-trip.com', 'http://deervalleycu.org', None, 'http://milkywaypgh.com', 'http://lemmeeatglutenfree.com', '1592598112', 'http://www.beadsinc.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://pizzaon40th.com', 'http://www.autobell.com', None, 'https://www.pizzahut.ca/store-details/store-R32808/pizza-hut-Markham', 'http://www.tinywardrobe.com/', None, 'http://www.jasauerco.com', 'http://teamoji.business.site', 'http://www.harperstire.com', None, None, 'https://www.redrobin.com', None, 'http://www.happypetslv.com', 'http://www.pizzerialibretto.com/', 'https://www.dormontflorist.com/?srccode=yelp_track', 'http://www.omarspmg.com', 'http://ramshaw.com', 'http://allsmilesaz.net/', 'http://www.gelatospot.com/', 'http://www.hihealth.com/storelocator/view?id=23', None, None, 'http://www.makeupbyrebecca.com', 'http://www.phoanh.ca', 'http://www.howon.ca', None, 'http://tropicanacaribbeancuisine.ca/', None, 'http://www.azvs.com/', None, 'http://www.chocolada.com/', 'https://www.wickliffeflorist.com/?srccode=yelp_track', 'http://www.azstrands.com', 'http://www.dentistryofthecarolinas.com/', 'https://www.cwsapartments.com/marquis-at-carmel-commons-charlotte-nc/', None, 'https://www.sephora.com/happening/stores/bramalea-city-centre', 'http://www.alvinavenuefootclinic.com', None, None, 'http://valueplace.com', 'http://local.biglots.com/az/phoenix/4085', 'http://www.hendersonlibraries.com', 'http://www.divinepoolsaz.com', 'http://www.hilldalebarbers.com', 'http://www.dnamydog.com', 'https://locations.vitaminshoppe.com/az/phoenix/vitamins-supplements-phoenix-az-210.html', 'http://www.natn-az.org/cup-okarma/', 'http://www.aprilgaybrealswellness.com', None, 'http://www.boltandspool.com', 'http://www.pittsburghparks.org', 'http://dogdaycareofmiddleton.com', 'http://www.orleanscasino.com/dine/bailiwick?disid=wmm_yelp_to_corporate_bailiwick_organiclink', 'https://locations.massageenvy.com/pennsylvania/monroeville/4124-william-penn-hwy.html', 'http://www.deervalleypc.com', 'http://www.entouragefitnessaz.com', 'http://www.easyautoglass.ca', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.johnbednarzpc.com/', 'http://www.sphysmed.com', 'https://www.usenergywindows.com', None, None, 'http://www.cityofhenderson.com/henderson-happenings/parks-and-trails/locations-and-features/cornerstone-park', None, None, 'http://www.rue21.com', 'http://www.jojo2go.com', 'http://www.lushusa.com', None, 'http://www.premiumoutlets.com/outlets/store_listing.asp?id=61', 'https://www.casinoarizona.com/dining/cholla-steakhouse-lounge/', 'https://mountainsidefitness.com/locations/arrowhead/', 'http://theburritofactoryclt.com', 'http://www.nandosmexicancafe.com', 'https://www.youfit.com', 'https://www.desertitsolutions.com', 'http://www.thethaigrill.com', None, 'http://www.dwellworks.com', 'http://www.sallybeauty.com', None, None, 'http://goldsgymcanada.com/', 'https://www.furniturestoreparma.com', 'http://hartwest.com', None, None, 'http://www.ticklemecomedy.com', 'http://www.manageyourpool.com', 'http://www.allstarwingsandribs.com', None, 'http://thelashandbeautyboutique.com', 'http://www.offthegriddle.biz', 'https://www.bhldn.com/pages/stores-pittsburgh', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.customcabinets4you.com', 'https://thepetclub.com/store/gilbert/', 'http://www.theclubatsunrise.com', 'https://www.chilis.com', None, 'http://www.capitalcrossingcharlotte.com', '1592598420', 'http://calgary.iflyworld.com', 'http://tix4tonight.com', 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', None, 'http://www.velvetbuttercream.com', None, None, 'http://mcithedoctorsoffice.ca/patients/37-clinic-Mt.-Pleasant', 'http://www.enclaveaz.com', 'http://www.fmautoexpo.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.plannedparenthood.org/health-center/arizona/tempe/85281/tempe-health-center-2808-90030?utm_campaign=tempe-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', None, None, None, None, 'http://www.myprohibition.com', None, None, 'https://www.signaturestyle.com/locations/pa/west-mifflin/cost-cutters-century-square-haircuts-15633.html', None, 'https://www.originalmattress.com/store/54/Matthews-North-Carolina-Store', 'http://www.dior.com', None, None, 'http://www.bluegrassnursery.com', 'http://www.tazhair.com/', 'https://www.choicehotels.com/north-carolina/charlotte/sleep-inn-hotels/nc084/rates', None, 'http://www.luxynails.ca', 'http://www.sushishop.com/', 'http://dsw.townshoes.ca/store/dsw/en', 'http://www.premierbuildersinc.com', None, '1592598534', 'http://www.dannysvacuum.ca/', None, 'http://www.biddulphmazda.com/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.a2zwatersystems.com', None, None, 'http://drlaffa.com', None, 'http://www.sportinglife.ca/', None, 'http://www1.toronto.ca/wps/portal/contentonly?vgnextoid=355cfe59abc61410VgnVCM10000071d60f89RCRD', 'http://www.ultimatefloorcareaz.com', 'http://www.activegreenross.com', 'http://www.maciam.com', 'http://pacificsales.com', 'http://www.epicthriftstores.com/', 'http://shanesribshack.com', 'http://www.tegacaywashandlube.com', 'https://www.agelessmenshealth.com/locations/henderson-testosterone-replacement-therapy-clinic/', None, 'http://kingsfamily.com/?utm_source=yelp&utm_medium=referral', None, 'https://local.fedex.com/az/mesa/office-1375/', 'https://www.pier1.ca', 'http://www.kfc.ca/store/27-ruth-ave-brampton', 'https://eosfitness.com/coming-soon-goodyear-gym?utm_campaign=%3Fgoodyear&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', 'http://www.starvingartistbar.com', 'http://www.aveda.com', 'http://www.zenmassagecharlotte.com', 'http://252tattoo.com/section/9075-COLUMBIA-STATION.html', 'http://www.sycamoreanimalclinic.net', 'http://www.artisticd.com', 'http://broadwaypizzerialv.com', 'https://www.interdent.com/gentle-dental/locations/az/surprise/13375-w-grand-ave-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.realsteemer.com', 'http://www.byobartafterdark.com', 'http://www.smartreit.com/shop/property/smartcentres-aurora-n-wellington-404/', 'http://deerval.com/phoenix.htm', 'http://www.stanleysfishandchips.com', 'https://locations.mrtire.com/oh/mayfield-heights/6680-mayfield-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://www.balenarestaurant.com', 'https://www.arcpointlabs.com/scottsdale-north', 'http://www.bellasolaralv.com?campaign_code=yelp_Bella_Solara_NV_89128', 'http://www.mypiada.com/', 'https://bookhouse.beer', 'https://www.target.com/sl/charlotte-se/918', 'http://earthwrks.com', 'http://www.starbucks.com', 'http://www.bangmadison.com', 'http://www.gpccinc.com', None, 'https://www.ferguson.com/branch/w-charleston-blvd-las-vegas-nv-plumbing', 'http://www.platinumpoochcle.com/', 'http://www.asiatiquethaibistro.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006430791762&ds_s_kwgid=58700000444978102&ds_url_v=2', 'https://eastcoastwings.com/location/denver-nc/', None, None, '1592598765', None, 'https://locations.panerabread.com/az/mesa/1946-south-signal-butte-rd.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://www.lastingskinsolutions.com', None, 'http://myugp.com/', 'http://www.streetsideclassics.com/locations/charlotte-north-carolina', 'https://bargainstorage.com/youngtown-bargain-storage/units', None, 'http://www.mooreandmore.com', None, None, None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://locations.wendys.com/united-states/oh/rocky-river/21250-center-ridge-rd.', None, 'https://www.torrid.com/store-details?StoreID=5319', 'http://famousnailsmesa.com', 'http://www.morrellparklv.com', 'http://www.duckanddecanter.com/', 'http://www.studiostaino.com', 'http://www.sparksgrill.ca', 'http://www.thecaptainsboil.com', 'http://affordablegarageaz.com/', 'http://www.abviphoenix.com/', 'http://www.roysrestaurant.com/locations/NV/las_vegas.asp', '1592598863', 'http://www.cchlv.com', 'http://graffitisocialkitchen.com', 'http://www.legacyhouseimports.com/html/tearoom.html', 'http://www.brakemasterslv.com/', None, 'https://stores.bestbuy.com/pa/munhall/680-waterfront-dr-e-882.html/?loc=ns100&ref=NS', 'http://www.starfootspa.com', 'http://www.directhardwoodfloor.com/', 'http://www.ahrmechanical.com/contact-us', None, 'http://eliterestorationlv.com', None, 'http://www.uslovesushi.com', 'http://www.pavilionbarbershop.com/', None, 'https://www.smallerscholars.com/schools/gilbert-az/?utm_source=yelp&utm_medium=local_listing&utm_campaign=yelp_website&cad_campaign=yelp_website', None, 'http://www.starnail.com/', 'http://annanailstempe.com/', None, None, None, 'http://www.verizonwireless.com/stores/ohio/fairlawn/fairlawn-333493/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'https://bilberryfreight.com', 'http://www.tatasushi.ca', 'http://www.thenewtonphx.com', None, 'https://www.cbac.com/happy-valley/', None, None, 'http://phokinghungry.com', 'http://www.dominos.com', None, 'http://www.allseasonsmarina.net', 'http://hairmasterssalon.com', 'http://www.eonmedicalspa.com', 'http://www.jj-lawnmowerrepair.com', None, 'http://www.myalida.com', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.sweetdaddycupcakes.com', 'https://www.focusmentalhealth.com', None, 'https://blumelasvegas.com', 'https://jancobookstore.com', 'http://www.stringzwingz.com/', 'http://mononagardenfamilyrestaurant.food-places.com', 'http://www.bestpetcare.net', '1592599034', None, 'https://www.gowireless.com/stores/az/gilbert/gilbert-gilbert-road/', 'http://bestoflvproperties.com', None, 'http://www.citywidetowing.com', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', '1592599058', 'http://www.thehubfitness.com', 'https://carnewbadetailing.com', '1592599066', 'http://www.caldergabroy.com', 'http://www.petsmart.com', 'http://www.starbucks.com/store/15887/', 'http://www.loolooshairsalon.com', 'http://piopiocharlotte.com/', 'https://www.famousfootwear.com/?partnerid=YELP', None, None, 'http://restobollywood.ca/fr/', 'http://www.fivestartransmissions.com', 'http://dailymaidscompany.wixsite.com/dailymaids', 'http://www.sabas.com/', 'http://arizonagoldexchange.com', 'https://www.purebarre.com/location/scottsdale-az', None, 'http://www.prochiroaz.com/', 'http://www.gianteagle.com', 'https://www.mayestelles.com', 'http://marbleslab.ca', 'https://somethin2talkabout.squarespace.com', None, None, '1592599148', None, 'https://www.lego.com/en-us/stores/?domainredir=stores.lego.com', '1592599162', '1592599167', 'http://calgary-movers.net', None, None, None, None, 'http://www.economylube.com', 'http://www.chicagodelisolon.com/', 'http://www.joshuahillscondos.com', 'http://www.bradystaxservices.com', None, 'http://palabraphx.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.homeoutfitters.com', 'http://www.tanontherun.com', 'http://www.petsmart.com', 'http://www.marriott.com/hotels/travel/cakmt-courtyard-akron-fairlawn', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.shylamagee.com', None, 'https://www.winterwonderfestaz.com/#expectations', 'https://www.pteglv.com/locations/pts-pub/stewart-nellis/', None, 'http://www.mangotours.com', 'https://totalback.com', 'http://www.remax.com', 'http://www.dontbebroke.com/?utm_source=Yelp&utm_medium=Location%2BPage&utm_campaign=Yelp', '1592599262', 'http://www.cafeparisaz.com/', None, 'http://www.marketlanevet.com/', 'http://www.davismagic.com/', 'http://acrobody.com', 'http://wet-tec.com/', 'http://azsls.com/', None, 'http://calibercollision.com/locate-a-caliber-collision-center/pineville', None, 'http://www.pandoralv.com', None, 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', None, None, 'http://www.marriott.com/hotels/travel/clein-residence-inn-cleveland-independence', None, 'http://insertcoinslv.com', None, 'http://www.redbox.ca/', None, 'https://www.aztechradiology.com', None, 'http://deluxedetailandtint.com/', 'http://www.t-mobile.com', 'http://www.vietfooddelivery.com/', 'http://www.zetsexpress.com', None, 'http://www.hopianimalhospital.com', 'http://www.kbdrywallrepair.com', 'http://17avenuevet.com', 'http://www.universityinnmadison.com', None, 'http://www.theflyingfig.com', 'http://www.madantopizza.com', None, None, 'https://stores.vans.com/az/chandler/8837/', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.signaturestyle.com/locations/az/anthem/cost-cutters-cost-cutters-haircuts-62206.html', 'http://www.cactuschiropractic.com', 'http://www.americanlaser.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=paid+search&BannerID=4772', 'http://www.leslievillecheese.com', None, 'http://www.madisonpubliclibrary.org/pinney', 'https://www.wyndhamhotels.com/hotel/02926?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:02926', None, 'http://reliablecabinetsaz.com', 'https://www.ibroken.ca', 'http://www.cadillacranchgroup.com/location/pittsburgh', 'http://www.velvetbuttonboutique.com', 'https://www.hmshost.com/brands/pork-pickle', 'https://www.urbanoutfitters.com/stores/cityscape-phoenix', 'http://salonfontanalasvegas.com', 'http://www.charlottecomfortsystems.com/', 'http://www.colourclinic.com', 'http://www.bluebirdbarbers.com', None, 'http://lgtauto.ca', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FLASGV', 'http://www.autorepairmesa.net', 'http://heidelrealty.com', None, None, 'http://www.tikkablvd.com/index.php', None, 'https://www.camdenliving.com/chandler-az-apartments/camden-pecos-ranch?utm_source=GMB&utm_medium=local&utm_campaign=Camden_Camden_Pecos_Ranch', 'http://www.heidisbrooklyndeli.com', None, 'http://www.newdayorganizing.com', 'http://www.ttc.ca', 'https://www.thejoint.com/nevada/las-vegas/eastern-and-richmar-36005', 'http://www.nyxcosmetics.ca', None, None, 'http://www.fhnaturopathic.com', None, '1592599536', None, None, None, None, 'http://plumberondemand.ca', 'http://www.shoelessjoes.ca/', 'http://www.johnnymalloys.com/location_strongsville.htm', None, 'http://mitchellsotka.com', 'http://www.bestbudsllc.com/contact-hoepker-rd', 'https://www.walgreens.com/locator/walgreens-29660+n+tatum+blvd-cave+creek-az-85331/id=3912', 'http://sirensandsaints.blogspot.com/', 'http://www.pulpkitchen.ca/', None, 'http://aimeearts.com', 'https://locations.timhortons.com/ca/qc/laval/3099-de-la-concorde-est.html', 'http://www.byersvacuum.com', 'http://www.butterandcup.com', 'https://www.flatsatsantan.com', 'http://www.vicu.utoronto.ca/hospitality/eventandspace/isabelbader.htm', 'http://www.OrthoAtDonMills.com', 'http://storefixturesandsupplies.com/', 'http://www.mnails.ca/', 'https://moxies.com/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', None, 'https://thaiexpress.ca', None, 'http://www.theeggandicafe.com/', None, 'http://www.secondcup.com/location/newmarket-18040-yonge-street', 'http://wingaddictionlv.com', '1592599642', 'http://www.asapcity.com', None, None, None, 'http://www.badgerbrothersmoving.com', 'http://www.angelos.ca/', None, 'http://www.southmountainpostacute.com', None, 'https://www.drwiitala.com', '1592599678', None, 'https://www.paylesscar.com/locations/pittsburgh-pit/', None, None, None, 'http://www.loxstockbagelaz.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'https://www.sunsetgrill.ca', None, 'http://dannystruckwash.com/', None, None, 'http://www.exxonmobilstations.com/18413-genins-mobil-service-madison', 'http://www.flowergirlflorist.ca/', None, None, 'http://www.bk.com', 'http://www.ezpawn.com', 'http://www.vegasacutherapy.com', 'https://the-diamond-group-home-inspections-inc.business.site', 'http://www.trutechinc.com/charlotte-animal-control.html', 'http://www.torontovetpet.com', 'https://shopgreatlakesmall.com/?utm_source=Yelp&utm_medium=Local%20Listings&utm_campaign=Yelp%20Listings', '1592599754', None, None, None, 'http://www.ama.ab.ca', 'http://www.harriscarsinc.com', None, '1592599772', 'http://www.freshnails.info', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://azoralsurgery.com', None, None, 'http://www.crossfittempe.com', 'https://www.askadamskutner.com', None, None, 'http://www.boomoptical.com', 'https://www.stvincentdepaul.net', None, 'https://www.lakeshorehotel.net', None, 'http://www.liuyishouna.com', None, 'http://yellowchilly.ca', 'https://www.penrosecharlotte.com', 'http://www.newrockstore.com/', '1592599846', None, None, 'http://www.canadarugbyleague.com/site/eng/', 'http://www.mpautobodyrepair.ca', 'http://www.verradogolfclub.com/', 'http://www.mattsmithpt.com', 'http://www.econrads.com', None, 'http://www.storyairways.com/', 'http://www.drkaus.com', None, 'https://www.bobevans.com/our-restaurants/locations/269?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'https://www.omnihotels.com/hotels/scottsdale-montelucia/spa?utm_source=yelp&utm_medium=sponsored&utm_campaign=phxrst-joya-listing', 'http://www.paradisecafe.ca', 'http://www.selfdefensevegas.com', 'http://www.glendalepowdercoating.com', '1592599899', None, None, 'https://www.cadence-academy.com/schools/charlotte-nc-mallard-preschool/?utm_source=yelp&utm_medium=local_listing&utm_campaign=yelp_website&cad_campaign=yelp_website', 'http://www.phoenixlongevityarts.com', None, 'http://www.ecigcityaz.com', 'http://www.tagsandtt.com', 'http://www.chevron.com/', 'http://innovativeaccesscontrol.com', None, 'http://www.allstoragevegas.com/locations/nevada/canyon-gate/?lid=3', 'https://west-island.modoyoga.com', 'http://bnelsondds.com', None, 'http://www.silveradoconstructionlv.com/', None, None, '1592599964', None, 'http://www.coldgarden.ca', 'http://7eleven.ca/store-locator/33259', None, 'http://www.huntersvilleeyecare.com', '1592599984', None, None, None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.pulte.com', 'http://www.eyecareplusaz.com/', 'http://www.bwfeye.com', 'https://www.bodibronze.com', '1592600015', 'https://www.clarendonparkapartments.com', 'https://www.calgarycoop.com/stores/shawnessy/', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3034+West+Lincoln+Avenue-Peoria-IL-61604/storeid=7798?cid=ps_ylp_2020', 'http://www.novasbakery.com/', 'http://todaystomorrowlearningcenter.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, 'http://www.toronto.ca/culture/victoria-square/index.htm', None, 'http://livemillennium.com', None, None, 'http://www.paitoronto.com/', 'http://originaloysterhousepittsburgh.com', 'https://www.oilvinegar.com/en-us/shops/chandler', 'http://apwservices.ca', None, None, 'http://www.chefgreywolf.com/', None, 'http://www.westernreservemeadery.com', 'http://www.thepixieplanner.com', 'http://www.villageinn.com', '1592600107', 'http://www.facesbeautyispower.com/', 'http://www.purplepoochie.com', 'https://www.arizonacleaning.net', None, 'http://kroran.business.site', 'http://www.yourautoservices.com', 'http://www.ginalouisadesigns.com', 'http://www.agavepediatrics.com', 'http://www.starbucks.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.tuffycharlotte.com', 'http://www.bellautoservice.com', 'http://www.mamameatballspizzeria.com', None, 'https://www.amctheatres.com/movie-theatres/pittsburgh/amc-classic-south-hills-village-10?utm_uid=yelp', 'https://www.platinummitsubishi.com', None, None, 'https://www.petsmart.com/stores/us/az/mesa-store0135.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', None, 'http://coldpressexpress.com', 'http://www.upmccancercenter.com/network/upmcpassavant.cfm', 'https://www.mrbaffo.com', '1592600185', None, None, 'http://willisskiandboard.com/store-locations', 'http://www.kascopm.com', 'http://www.apricotlounge.com', 'https://www.gorefreshdental.com/locations/refresh-dental-westlake/', None, 'http://www.wholesaleclub.ca/LCLOnline/store_details_landing_page.jsp?storeId=501', 'http://neddataxaccountant.com/', 'http://tveh.ca', 'http://www.nextcare.com/locations/az/tempe/?utm_source=Yelp&utm_medium=Local&utm_campaign=tempe', 'http://www.thatsitaliantoo.ca', 'http://app.cat', 'http://www.wjproperties.ca/', 'http://oasisdentistry.org', 'https://order.freshii.com/us/en-us/330-dundas-oakville', 'http://www.dunkindonuts.com', 'http://www.heartlandnursing.com/Willoughby', None, 'http://www.jonathanadler.com', 'http://weezies.ca/', 'http://www.zinburgeraz.com/locations/phoenix/', None, 'http://www.starbucks.com/store/14763/', 'http://www.lvvhumane.org/', None, None, 'https://parkmgm.mgmresorts.com/en/nightlife/mama-rabbit.html', 'http://www.ronlewischryslerdodgejeeprampleasanthills.com', 'http://www.aladdinseatery.com', 'https://www.braesideon24th.com', 'http://saralasvegas.com', 'http://www.valleyhospital-phoenix.com', 'http://ecocleanerslv.com', 'http://greathousesportspt.com', 'http://www.cafesympatico.com/', None, 'http://www.escapehourcharlotte.com', None, 'http://acexpertek.com', 'http://www.brianspoolcare.com/', 'http://tiffanyandco.tumblr.com', 'http://www.directrepaircollisioncentres.ca', None, None, 'http://www.serranosaz.com/html/serranos/', 'http://www.lilyshsalon.com', 'https://pswsunglass.com', None, 'https://www.lhshealth.com/facility-locations/pleasant-lake-villa/', None, None, 'https://piedmontdentistrysmiles.com', None, 'http://www.oasisbehavioralhealthlv.com', 'http://www.acuraeast.com', 'https://800degrees.com/locations/', 'https://ultimatedrivers.ca', 'http://m.mainstreethub.com', 'http://www.midfirst.com', None, 'http://www.radiantchurch.com', '1592600403', 'http://www.uni-tech.com', None, 'http://www.MomDocWomensHealthResearch.com', 'http://www.airportinfiniti.com/', 'http://www.twinimagehairdressing.com', 'https://www.mountainscapers.com', 'http://www.bedbathandbeyond.com', 'http://gritandgracepgh.com/', None, 'http://www.greatlengths.ca', 'https://www.wittpm.com', None, 'https://locations.theupsstore.com/oh/shaker-heights/16781-chagrin-blvd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.lonestartexasgrill.com', '1592600461', None, 'https://www.gerbercollision.com/locations/huntersville-nc', None, 'http://www.stakeoutdining.com/', '1592600477', 'http://durangohighschool.net', 'http://www.unos.com', 'http://www.einsteinbros.com', 'http://www.tuesdaymorning.com', None, None, 'http://www.bk.com', 'http://www.theslip.ca', 'https://www.choicehotels.com/north-carolina/concord/comfort-suites-hotels/nc392/rates', None, 'http://www.keystonemontessori.com', 'https://www.tomyamthai.ca', 'https://www.catalystfitaz.com', None, 'https://www.makeitshinehomecleaning.com/our-services', 'https://www.hertz.com/', 'http://www.youngazpeds.com', None, 'http://www.topshop.com', 'http://aureliospizza.com', 'http://www.armstronganimalclinic.com', 'http://LakeNormanDentist.com', 'http://www.thespicevillage.ca', 'http://www.westernsageinsurance.com', None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.chick-fil-a.com/wesleychapelweddington', None, 'http://www.tungtungdanquenking.com', None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', '1592600598', 'http://www.allstarwingsandribs.com/', 'https://shaganappigrocery.com', '1592600609', None, 'http://www.roccos-pizza.com', None, 'http://benetflorentine.com', 'http://www.homecareassistancescottsdale.com', 'https://www.turntwoauto.com', 'http://www.dlcphoenix.com', 'http://craftmerchandiseinc.com', 'http://www.babyandmematernity.com', 'http://www.thrifty.com/?campid=DS:YL_THR_20150109_HP', None, 'http://www.orkin.com/', '1592600656', 'http://www.preferredtrustcompany.com', 'https://www.theventuraapts.com', None, None, 'http://www.northfieldpark.com', 'https://stores.jcrew.com/en/j-crew-yorkdale', None, None, 'http://www.threeriversyoga.com', 'http://www.zpizza.com', None, None, 'http://www.ptcenterakron.com/', 'http://www.pressurewashlv.com', 'http://www.hightechheatingandac.com', None, 'http://www.dreamingant.com', None, 'https://www.walmart.com/store/5339/pittsburgh-pa/whats-new', 'https://altitudegilbert.com', 'http://www.getthelicense.com', 'https://www.friartux.com/store-locator?utm_source=Yelp+Website', 'https://www.renthpmotors.com', 'http://goldstarfinancial.com/jorgealvarez', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.lvappliancerepairs.com', 'http://www.iloristyle.com', None, None, 'http://www.angelstrumpetalehouse.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'https://www.chick-fil-a.com/arboretum', None, 'http://www.lalaphotography.com', 'https://www.xfinity.com/local/pa/pittsburgh/5211-brownsville-road.html', None, 'http://www.allyouneedmovingllc.com', 'http://www.dogtopia.com/charlotte/', 'https://www.divineidea.net/', 'https://www.interstatebatteries.com/locations/all-battery-center-las-vegas-nv', '1592600786', 'http://www.1992sharetea.com', 'http://steelespaint.com', 'https://www.theaudreykitchenandbar.com', 'http://www.taxcontroversy.com', None, None, None, 'http://www.proglassaz.com/', 'http://www.southsidetattooshop.com/', 'http://www.temp-rite.us', None, 'http://www.johnwardmd.com', None, None, None, 'http://www.freddysusa.com/locations/?distance=25&address=85284', 'http://www.comwave.net', 'http://www.citytannc.com', 'https://luxenailbar-nailsalon.business.site', 'http://www.mindzai.ca', 'http://anailsnspa.com', 'https://www.integratedmovingservices.com', 'https://agents.farmers.com/nv/las-vegas/joseph-haas?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.ccv.church', 'http://redfoxsportspubandgrille.com', 'http://www.themargaritahut.com', 'http://www.oaidocs.com', None, None, 'http://www.pimasuites.com', 'http://www.fluffyspa.com', 'https://fast-tracdesigns.com', None, 'http://www.bigcityburgersavonlake.com', None, None, 'http://www.apartyplacerentals.com', None, 'http://www.harpersgroup.com', '1592600918', None, 'http://horizonwomenshealth.net', 'http://www.embetc.com', 'http://www.novusclinic.com', None, 'http://www.saltriversurgeons.com', 'http://www.kochibythelake.com', 'http://www.piccolo-forno.com', 'http://woodfirepit.com', 'https://www.walmart.com/store/2512/phoenix-az/details', '1592600957', 'http://www.healthpointcs.com', 'https://www.ecoshieldpest.com/landers/general-pest-control/?utm_source=yelp&utm_medium=website&utm_campaign=organic&location=6695', '1592600970', 'https://symposiumcafe.com/locations/uxbridge-restaurants', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.greatclips.com/', 'http://www.alishawadeaz.com', None, 'http://nhuptownprimarycare.org', 'http://www.madisonpubliclibrary.org/pinney', 'http://www.amicihair.ca/index.html', 'https://eastcoastwings.com/location/9711-northlake-centre-pkwy/', 'http://www.laveencountrydoc.com', 'http://www.avelorestaurant.com', 'http://www.desertspringsdentalcare.com', 'https://www.snowyvillages.ca', 'http://friendshipfoodstores.com/StoreHome/93', 'http://www.urbansun.ca', 'https://locations.wafflehouse.com/az-tempe-1797', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.touchohiocity.com', 'http://themillbarandgrill.ca/', None, 'http://www.kopperkegLV.com', 'http://www.secondcloset.com', 'https://stores.musicarts.com/charlotte?source=LGOA5LKA', 'http://www.beeskneesdance.com/', 'https://newyouspas.com', 'http://ciaoitaliancafe.com', None, None, 'http://lasvegasdoulaservices.com', 'https://www.theflatsatarrowood.com', 'https://www.udadentistry.com/practices/university-dental-associates-northlake?utm_campaign=Organic&utm_medium=Listings&utm_source=Yelp', 'http://steakandchops.ca/', 'https://www.petparadise.com/phoenix.htm', 'http://www.gvdentalgroup.com', None, 'https://www.signaturestyle.com/locations/wi/madison/cost-cutters-cost-cutters-haircuts-17372.html', None, 'http://gwisemanlaw.com', 'http://locations.atipt.com/phoenix-az', 'http://www.caliahair.com', None, 'http://www.fandflame.com', 'http://lfmarketaz.com', 'http://Pamairllc.com', None, 'http://peters-hairstyling-barber-shop.business.site', 'http://www.reclaimchurch.com', 'https://www.crossingsonmain.com', 'https://www.frysfood.com/storeHours?store=66000064', 'https://deserteagletowing.com', 'http://www.triplecrownbar.ca/', None, None, None, None, 'http://www.bossanovapgh.com', None, 'http://www.hopkinsfamilychiropractic.com', None, None, None, None, None, 'https://sunnynailstallmadge.com', None, 'https://www.boydautobody.com/locations/calgary-1st-st-ab', 'http://www.mersingrill.com', None, None, 'http://www.einsteinbros.com/', 'http://www.goochipoochi.net', None, 'http://www.mafiamikespizza.com/', None, None, None, 'http://yourhelpinghandsvegas.com', None, 'http://mahoneysrestaurant.com/', 'http://www.theedgeaz.com/', 'https://www.copaair.com', None, 'http://resort.to/vegasfortuna', 'http://www.innerpeaks.com/', 'http://www.bangerbrewing.com', None, 'http://www.desertvalleyconcepts.com/', 'http://www.mybackontrack.com', 'http://integrityoutsource.com', 'https://www.cricketwireless.com', None, '1592606676', 'https://www.campervannorthamerica.com/location_las-vegas.shtml', None, 'http://www.heartlakecleaners.com', 'http://www.crazymocha.com', 'http://www.checksmart.com', None, None, 'http://www.mandarinsuperbuffet.com', None, 'http://www.scientology-toronto.org', 'http://www.gabyetjules.com/', 'http://www.fairviewdentistry.com', 'http://www.biltmoresquare.net', '1592606705', None, 'http://www.searsauto.com', None, 'http://www.vegasrollingshuttersandpatioshades.com', 'http://www.ciboevinoaz.com', 'http://www.scottclarkstoyota.com/?utm_source=yelp&utm_medium=business_url&utm_campaign=local-citations', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZSB', None, None, None, None, None, None, 'http://www.bk.com', 'https://www.tlcvision.com/centers/toronto/?eventid=6880', '1592606744', 'https://www.aearizona.com', None, 'https://smashburger.com/?utm_source=yelp&utm_medium=organic', None, 'http://tc2go.com', 'http://www.petplanethealth.com/stores/country-hills-town-centre/', 'http://www.anthonyphotostudio.com', 'http://www.cloverdalemall.com', '1592606766', None, 'http://www.overcoffeeonline.com', 'http://www.beauty-exchange.com', None, '1592606776', 'http://www.sprint.com', 'http://www.excelchiropracticlv.com', None, 'http://www.perfecthomefurniture.com', 'http://reddispizza.com', None, 'http://www.obgynarizona.com/', 'http://azarthritis.com', None, 'https://www.modernbodyclinic.com', 'https://www.zoup.com', 'http://www.legacyvideography.com', 'http://www.takefivedance.com', 'http://madisonsdowntown.com', None, None, None, '1592606819', 'http://www.grecofitness.com', 'http://lotsalovinpetsitters.com/index.html', None, 'http://starkaraokeuiuc.com', 'http://www.alternativesolutioncarcare.com', None, 'http://www.growbosslv.com', 'https://www.eyedoctorintoronto.com', None, 'http://www.jimandersonauto.com', None, None, None, 'http://maddpretty.com', 'http://99sudbury.ca/Gym/', 'https://www.theparkingspot.com/locations/charlotte/clt/the-parking-spot', None, 'http://ameribailbonds.com/', 'http://www.mesadentalhealth.com/', None, None, 'http://www.JONCENPHI.com', 'http://www.urbannails.ca', 'https://www.roche-bobois.com/en-CA/showrooms/calgary', None, None, None, 'https://www.walgreens.com/locator/walgreens-10140+w+colfax+ave-lakewood-co-80215/id=9887', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.bajachuys.com', 'http://www.devillecoffee.ca/', 'http://www.acevaper.ca', 'https://www.nvenergy.com', None, 'http://doralacademynv.org', 'http://wirelessphonemedicslv.com', 'http://www.hobbyprodigy.com', None, 'https://www.bostons.com/locations/index.html?location=Wisconsin', 'http://www.honest-1.com', 'http://phoenix-eastthomas.redwingshoestore.com', None, 'http://www.menchies.com', 'http://www.landmark.coop', '1592606933', 'https://fr.starbucks.ca/store-locator/store/1017410/41-boulevard-de-la-cite-des-jeunes-41-boulevard-de-la-cite-des-jeunes-vaudreuil-qc-j-', 'http://www.ubreakifix.com/locations/lasvegas', 'http://www.taoofwomen.com', 'http://www.antheia.ca/', 'http://www.primemoving.pro', 'http://www.actux.com', 'http://www.dontortaco.com', 'http://www.dlkonavenue.com/', 'http://www.mitchellchiropracticaz.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'https://www.pigeonsbegone.com', 'http://www.jerkyking.ca/', 'http://www.verizonwireless.com/stores/pennsylvania/pittsburgh/pleasant-hills-1306622/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://www.bulwarkpestcontrol.com/', '1592606972', 'http://www.cakebakeshoppe.ca', '1592606978', 'https://www.rounderslv.com', 'http://www.chiangmaithaimassagelv.com', 'http://lepaindanslesvoiles.com', 'https://mypiada.com/menu/oakland', 'http://wasabiteriyaki.wordpress.com/', 'http://www.smoothieking.com', None, None, 'http://a1upholsterycharlotte.com', None, None, None, 'http://www.bswsuperstores.com/las-vegas', 'http://www.cafesupreme.com', 'http://www.hottopic.com', 'http://www.headshotsaz.com', None, 'http://charlotteathleticclub.com/', None, 'http://mertsheartandsoulcharlotte.millionsofcafes.com', 'http://www.josephbeth.com', 'https://www.cranberryhillscafe.com', 'https://www.grandcanalshoppes.com/en/directory/welcome-to-las-vegas-3633.html', None, None, 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'https://www.davidsbridal.com/?utm_source=Yelp&utm_medium=OrganicSearch&utm_term=28&utm_content=DisplayURL&utm_campaign=WebsiteListing', None, None, 'http://themiller.ca', None, None, None, 'http://www.strengthtrainingrehab.com', 'http://www.wyldchyldpittsburgh.com/', None, 'http://www.rotorooter.com/champaign', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.empire-ink.com', None, None, None, 'http://www.bathandbodyworks.com', 'http://www.songbirdcoffeehouse.com/', 'http://www.pavilionhospital.com', None, 'http://www.torrid.com/store-details?StoreID=5033', 'http://www.tgiflowers.com', None, 'http://www.knightsinn.com/hotels/hotel-overview?hotel_id=07461&tel=18884240138&wid=fe:kg:20160215:yl:pp:kg:07461', 'http://www.greenimpressionslandscape.com', 'http://thaiauthenticmassage.com', 'http://trampalina.webs.com/', 'http://www.highlandschurch.org/', 'http://drkenshah.com', None, 'http://topfloorcleaners.com', 'http://imalv.com/home', 'http://www.peets.com/?cm_mmc=yelp*peets*8_28_12_homepage*na', 'http://www.thepintlasvegas.com', 'http://azhandman.com', 'http://www.2golf.ca/', '1592607125', None, None, 'http://www.changessaloninc.com', 'https://www.ubreakifix.com/locations/scottsdale', 'http://www.finefinishautodetail.ca', 'https://www.rolex.com', None, 'http://204north.com', 'http://heflinlawplc.com', 'http://www.federicosmexicanfood.com/', None, None, 'http://www.jessiespainting.com', 'http://saborcharlotte.com', 'http://www.gatewayvillage.com/main.cfm?pid=ocrrservices&sid=amenities', 'http://www.museumofthenewsouth.org/', None, 'http://www.thecrest.ca/', '1592607172', '1592607174', None, 'http://www.freshii.com', None, None, 'http://www.albahairlounge.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.drhudson.com/', 'http://www.fuzzystacoshop.com', '1592607196', 'https://megafurnitureusa.com', 'http://www.krispykreme.com', '1592607204', 'http://stores.sunglasshut.com/us/oh/westlake/279-crocker-park-blvd.html', 'http://houseboync.com/', None, 'https://www.servprosouthcabarruscounty.com', None, 'https://redrock.sclv.com/Dining/8-Noodle-Bar?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', None, 'http://www.carterpowersports.com', 'https://www.walgreens.com/locator/walgreens-27251+wolf+rd-bay+village-oh-44140/id=10029', 'http://www.bakerpoolsaz.com/', 'http://www.fcc-phx.com', 'https://bobmooretireservice.com', 'http://www.parkterracephoenix.com', 'http://www.vaughanpl.info', 'http://www.lola-bistro.com', 'http://www.sunbuggy.com/lasvegas', None, 'http://www.nomadshop.net', None, 'http://www.lilysanzphotography.com', 'http://www.CamilleFlawless.com', 'https://www.tangeroutlet.com/glendale', None, None, 'http://www.spincitycoinwash.com', 'http://www.cadillacranchtempe.com/', None, 'http://www.bigalscanada.com/Stores/Locations/Whitby/whitby.html', None, None, 'https://www.ironwoodanimalhospital.com?utm_source=yelp&utm_medium=Business&utm_campaign=IronwoodAnimalHospital-CallNow', 'http://www.pcamlv.com', 'https://www.artinstitutes.edu/closed-school-information-page', None, None, 'http://www.pandora.net/en-us/stores/united-states/85295/pandora-santan', 'https://www.tgifridays.com/locations/1545/fridays-cleveland-westlake-ohio', 'https://www.constellationliving.com', None, 'http://vtheaterboxoffice.com/Vegas_Show_Tickets.cfm?showID=10015', 'http://www.playmayfield.com', '1592607304', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.courtyardtowersaz.com', None, None, 'https://topgolf.com/us/las-vegas/', None, None, 'http://www.dunkindonuts.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', 'http://www.tigerdirect.ca', None, 'http://rockinbettie.com/', 'http://www.familyautodiesel.com/', None, 'http://www.alankrealtygroup.com', None, None, None, 'http://www.tatumeyecare.com', None, '1592607370', None, None, None, 'http://www.harryanddavid.com?cm_mmc=stores-_-yelp-_-533-_-link', 'http://breakfastjoynt.com/', 'http://www.kwiktrip.com/', 'https://www.larsonhomeservices.com', 'http://www.aprofessionallocks.com/', None, None, None, 'http://www.azlaptoppros.com/', 'https://meltbymelissa.com', 'http://www.casanovabites.com', 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://www.nimana.com', None, 'http://www.moonvet.com', None, 'https://www.key.com', 'https://local.biglots.com/il/champaign/438?zcp=pd_local_yelp', 'https://www.lampsplus.com/stores/arizona/chandler-85226/?sourceid=SMYELPTXLKStore42&cm_mmc=YELP-SM-_-Text-_-Link-_-Store42', None, None, '1592607425', 'http://homeairconditioninglv.com', 'http://www.pineappleparklv.com/', '1592607432', None, None, None, None, None, 'http://www.the519.org/fabarnak', 'http://www.wallingteam.com', None, 'http://www.fixt.ca', '1592607457', None, 'https://www.eliteheatingandac.com', None, None, None, 'https://www.180smoke.ca/vape-shop-etobicoke-islington-electronic-cigarettes', 'http://7eleven.ca/store-locator/14812', 'https://www.jimmarshkia.com', 'http://www.lwchiropractic.com', 'http://infinitevapor.com', 'http://www.sonicdrivein.com', 'http://www.oasishookahlv.com', 'http://www.southstburger.com/location/laird-and-wicksteed/', 'http://www.organiquejuicebar.com', 'https://doctorscare.com/indian-land', None, None, None, None, None, '1592607514', '1592607518', 'http://www.planetfitness.com/gyms/gastonia-nc-194?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.rolfssalon.com', 'http://www.vibrantcare.com', 'http://www.liveatgleneagles.com', None, 'http://www.gamestop.ca', 'http://www.thederrickyyc.com', 'http://C5PMAZ.com', 'http://homerhandyman.com/', 'http://www.chiromotion.ca', None, 'http://hot-shop.ca', 'http://www.northvalleymartialarts.com', 'http://mrvolvoplus.ca', 'https://www.fetchpetcare.com/champaign-urbana', '1592607578', 'http://www.arrowfurniture.com/locations-scarborough/', 'http://www.ccv2rx.com', 'http://bk.com/', 'http://www.theflyingelephantbakery.com/', 'http://www.chinaharvestbuffet.com', 'http://www.firespicegrill.com', 'http://www.vitense.com', 'http://clicks.dbm-media.com/Yelp_mobile', 'http://www.baskinrobbins.ca', 'http://www.CrossFitIncendia.com', 'http://www.magicsteam.net/', 'http://vipsitters.com', 'http://www.tilttoronto.com', 'http://pizzaiolle.com/ville-mont-royal', None, 'http://www.ahwatukeeskincare.com', 'http://www.designingaz.com', None, 'http://www.7-eleven.com/?yelp=29384', None, 'https://www.carx.com/champaign/2216-s-neil-st/', 'http://www.guildmortgage.com/officers/donnajobennett.html', None, 'http://www.muchoburrito.com', 'https://www.amctheatres.com/movie-theatres/phoenix/amc-dine-in-desert-ridge-18?utm_uid=yelp', None, 'https://kegsteakhouse.com/en/locations/newmarket', '1592607677', 'http://www.redrock-automotive.com', 'http://www.hcpnv.com', None, None, None, 'http://www.dignityhealth.org/medical-groups/WF_FindADoc_Profile.aspx?id=85c63192-78a8-4fe0-9403-fa21354a7108', 'http://inkbeautybar.business.site', 'https://locations.theupsstore.com/wi/madison/4230-east-towne-blvd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.breadsmith.com/', None, 'http://www.stellasofmadison.com', 'http://www.sanremospizzapgh.com', 'http://www.rivercruiserkayaking.com', None, 'https://2030bubbleteacafe.com', '1592607731', 'http://www.starbucks.com/store/9334/', 'http://www.evictionking.vegas', 'http://www.pinkbandanabakery.com', 'http://www.print2go.ca/', None, 'http://stripchezze.com', '1592607753', 'http://www.lewisinteriors.com', None, 'http://www.flowersbycc.com', None, 'http://www.dsw.com', 'http://www.arteefabricsandhome.com', 'http://www.schlotzskys.com/', 'http://www.cleanfreakcarwash.com', None, 'http://runyonappliance.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4755+West+Ann+Road-North+Las+Vegas-NV-89031/storeid=2989?cid=ps_ylp_2020', 'http://www.officedepot.com', 'http://imalv.com/home', 'http://gordosdiner.com/', 'http://www.aquamarineofhenderson.com', None, 'http://www.bostonpizza.com', 'https://classyclosets.com/scottsdale-arizona/', 'http://avis.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://www.bodyworks-tattoo.com', None, 'http://doughboysaz.com/', '1592607835', 'http://www.scottsdalehydrotherapy.com', 'http://www.workhorselv.com', None, None, 'http://www.permanentmakeupmichelle.com', 'http://www.revolutiondancecalgary.com', 'http://libertyshawarma.com', 'http://www.phoenixareasingles.com/', 'https://www.williams-sonoma.com', None, 'https://pizza.dominos.ca/l-Ile-Perrot-Quebec-10660/', 'https://groceryoutlet.com', None, 'http://www.fixitfloyd.com', None, 'http://www.avondaleautocenter.com/', 'http://www.acehardware.com/', None, 'http://krusesbakery.com', 'https://thegoodberry.ca', 'https://www.ancalacc.com', 'http://www.UnitedBeautySupply.com', 'https://www.archerdental.ca/locations/archer-dental-rosedale/', None, 'https://www.jackofdiamondsautobody.com', '1592607919', 'http://www.cornerstonekidzaz.org', 'http://www.SafeLifeDefense.com', 'http://www.urbanathletecalgary.com/', 'http://bubblerepublic.ca/', None, 'http://www.riverstarrestaurant.com/', 'http://oakhillkennelllc.com/', 'https://www.havertys.com/furniture/allstores/north-carolina/charlotte/carolina-place?cm_mmc=Local-_-Business-_-Listing-_-Citation', 'http://www.skinhavenesthetics.com', 'http://www.morningglorybrunchery.com', 'http://www.alertcleaning.com', 'https://calgary.worldhealth.ca/location/richmond/', None, '1592607963', 'http://www.elmolcajeterestaurantsc.com', 'https://www.kokopelligc.com', 'http://www.searsoutlet.com', 'http://www.helloglotan.com', 'http://local.firestonecompleteautocare.com/arizona/glendale/3540-w-bell-rd/?lw_cmp=IYP_YPC_MLP_11940', 'http://www.planetsupersaver.com', '1592607991', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.mohawkflooring.com/carpet-store/Calgary_AB_T3G-2T5/Floors-on-Crowfoot?utm_source=Yelp&utm_medium=Web&utm_campaign=MohawkYelpProgram', None, 'http://www.BOLDRealEstateConsultants.com', 'http://www.charlottenutritionandwellness.com', 'https://www.diamondchemdry.com', None, 'http://www.mitchellschocolates.com/', 'http://www.cabanasislandrestaurant.com', None, 'http://desertrocksportslv.com/', 'http://pier51concord.com', None, None, 'http://www.otanishiatsuclinic.com/', 'http://www.saltcreekhomefurniture.com', 'http://www.medicathehealingarts.com/', None, None, 'http://www.redtag.ca', 'http://www.mollybrannigans.com', 'http://quickfixmedina.org', 'http://revolutionvegas.com/', 'https://www.clubpilates.com/monroestreet/', None, 'http://www.ephesuspizza.com', 'http://www.ayascottsdale.com', 'https://www.marriott.com/hotels/travel/phxcn-courtyard-scottsdale-north/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=626&utm_content=bpas', 'http://www.foothillsrehab.com/', 'http://inksinstallation.com', 'https://secure.ssa.gov/ICON/ic001.do#officeResults', None, 'http://www.customairspecialists.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.starbucks.com/store/9289/', None, None, None, 'https://www.kiaofstouffville.ca', 'https://www.walmart.com/store/2266/strongsville-oh/whats-new', None, 'http://www.stratigosbanquet.com', None, None, 'http://mkautomotive.com', 'http://www.beckersbridals.com/', None, 'http://www.achiropractichealing.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'http://www.blondieslasvegas.com', None, 'http://www.allmobilematters.com/stores/chandler-fashion-center/', 'https://www.jugojuice.com', 'http://www.bluebutterflyms.com', 'http://www.bloompharmacy.ca', 'http://www.griplv.com', 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', None, 'http://www.godavarius.com/charlotte', 'http://www.ihg.com/staybridge/hotels/us/en/mayfield-heights/clelc/hoteldetail', 'http://pyramidelectricservice.com', None, 'http://www.yellowcabofcharlotte.net', None, None, 'https://www.walmart.com/store/2506/ravenna-oh', 'http://uniqueindianboutique.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXTD', 'http://www.maximumcomics.com', None, 'http://kindexchange.ca/', 'http://lakemeadauto.com', 'http://www.urologyspecialistsnc.com', 'http://www.starbucks.ca', 'http://www.chopit.com', 'https://www.californiaclosets.com/request-a-free-design-consultation/?utm_source=Yelp&utm_medium=cpc&utm_campaign=NV123A&utm_content=PRO&CC0=Yelp&CC3=NV123A&CC5=30007&CC6=30599', None, 'http://www.greekpatio.biz', 'http://conklinpaintingaz.com', 'http://www.exoticplantworks.com', None, 'http://www.andrewsfineviolins.com', '1592608278', 'http://www.djssmokeshop.org', 'http://bluezonepools.com', 'http://www.michellesforever.com', 'http://www.bankofamerica.com', '1592608297', 'http://atwellinvestigations.com', 'https://incha761bay.business.site', 'https://sitmeanssit.com/dog-training-mu/swlv-dog-training/', 'http://www.starbucks.com/store/1010275/', 'http://www.redwoodpetresort.com', 'http://www.BrianVSellsAZ.com', 'https://www.tracyriggssalon.com', 'http://www.lasvegas-cosmetic-dentistry.com', 'http://www.totalbodyrehabaz.com', 'https://www.lasikmd.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=mississauga&utm_content=general-link&p_utc=YELP_paid', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.migueldemaria.com', '1592608346', 'http://sharpedgebeer.com', '1592608355', 'http://www.desertpinesgolfclub.com/course/duffers-restaurant/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592608368', 'http://www.4cats.com/inglewood', 'http://www.alka1.com', '1592608378', None, 'http://youngsfinefurniture.com', 'http://www.queenelizabeththeatre.ca', 'http://Brunospizzavegas.com', 'http://www.phoenixraceway.com/', 'http://nestlecafe.com', None, None, 'http://www.gamestop.com/store/us/az/scottsdale/2760/sonoran-village-gamestop', 'http://www.heinzlofts.com', '1592608416', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=phxff&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', None, 'http://www.papajohns.com/', None, 'https://organiccleanersaz.com', None, None, 'https://stores.joann.com/az/phoenix/1917/', 'http://www.sacredtouchchiropractic.com', None, None, None, None, 'http://www.gracevet.com', 'http://www.randstad.ca', 'http://www.streetsofnewyork.com', None, None, '1592608477', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.target.com/sl/mentor/2322', '1592608487', 'http://happygardenmedina.com', 'http://www.tonysplacenv.com', 'http://TwoHeartsNails.com', 'http://www.azsedans.com', None, 'http://www.protection1.com/local/nevada/home-security-nv-las-vegas', None, None, None, None, 'http://www.channingmurray.org/redherring', None, 'http://mrgreek.com', 'http://locations.daltile.com/nc/charlotte/221', 'http://mteverestcuisine.com', 'http://www.donili.com', 'http://eastcoastcustard.com', None, None, 'https://locations.dennys.com/NV/LAS-VEGAS/247828', '1592608561', 'http://www.rivertradingpost.com', 'http://www.puremedspa.com', 'https://thedjcrewoh.com', None, None, 'http://www.greatclips.com/salons/9261', '1592608584', 'https://matthewsfun.org/OurParks/SquirrelLakePark/tabid/181/Default.aspx', 'http://www.siteprosolutions.com', 'http://www.charlottetailgatemarket.com', 'http://www.affinitycarrentals.com', 'http://www.mayasgold.com', None, 'http://www.tarheelappliancerepair.com', 'http://www.bushmaster.ca', 'http://www.fifthavevw.com/', None, 'http://Ledezmaselectronics.com', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.robiburnsmd.com', 'http://www.sleepingbeautyaz.com/', None, None, None, 'http://www.ultraautosound.ca', 'http://www.ljsilvers.com', None, 'http://www.knotsphoenix.com', None, 'http://www.mikhailusa.com', 'http://www.capitalwestins.com', 'http://staples.ca', None, 'http://www.thewigcottage.com/', 'http://www.cannerywineandspirits.com/', None, None, None, 'https://www.walgreens.com/locator/walgreens-6649+morrison+blvd-charlotte-nc-28211/id=1376', 'https://www.ihg.com/holidayinnexpress/hotels/us/en/medina/mdioh/hoteldetail', 'http://mrroofrepair.ca/', None, 'http://www.broadviewdentalclinic.com', 'http://www.skinawakened.com', 'http://www.blm.gov/nv/st/en/fo/lvfo/blm_programs/blm_special_areas/red_rock_nca/recreation/red_rock_campground.html', None, 'http://www.pitaland.ca', None, 'http://www.carolinashealthcare.org/', 'http://www.joescrabshack.com/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.hottopic.com', 'http://www.hp2promo.com', None, 'http://www.mcneillybeer.com/', 'http://www.barriourbanophx.com', 'http://www.leonidas-chocolates.ca/', '1592608765', 'http://microsoft.com/en-us/store/locations/pa/pittsburg/ross-park-mall/store-1057?pointit_retailsustain_sitelinks_Yelp', 'http://vegasdermatology.net', None, 'http://www.loblaws.ca/en_CA/storedetail.431.html', None, 'http://www.lisascosmetics.com', 'https://www.merryhillschool.com/elementary/las-vegas/durango-dr/?utm_medium=directory&utm_source=yelp&utm_campaign=paid_listing&utm_content=website', 'http://autodesignsvegas.com/', 'http://blomedry.com/locations/blo-bloor-west-village/', None, 'https://tanfx.ca/locations/tan-fx-calgary-shepard/', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.birraburger.com', 'http://www.garygarrettinsurance.com?cmpid=B696_BLM_0006', None, None, None, 'http://www.canadajunk.com', 'http://www.yogurt-land.com/', None, 'http://www.subaruofchampaigncounty.com', None, 'http://goodtastehousechinese.com', 'http://homestylefurnishings.com/', 'http://www.surgispa.net', None, None, 'http://www.honestweight.ca', None, 'http://www.torontophysiotherapy.ca', 'https://www.palettegrill.com', 'http://www.lightworkersgifts.com', 'http://www.hottopic.com', 'http://www.uspatiorepair.com', 'http://www.greatclips.com/', 'http://locations.harristeeter.com/nc/huntersville/209/', None, 'http://www.centropizza.ca', 'http://www.copperstoneplumbing.com', '1592608913', 'http://gatewaysurgerycenter.com?cid=list_amsg_centers_yext_link_2017', 'http://www.indoorcomfortsupply.com', 'http://www.dlkdental.com', None, '1592608930', 'https://www.sheetz.com', 'http://www.cleanqueencleaningservices.com', 'http://www.InfinityMedWeightLoss.com', None, 'http://icuracao.com', 'http://celebritytanning.com', 'http://www.popmaizen.com', 'http://www.chocolato.com', 'http://www.hendersonlibraries.com/Green-Valley-Library', 'https://santafestation.sclv.com/entertainment', 'http://www.jamesplace.co', None, 'http://www.theteamaison.com', 'http://www.carolinasmedicalcenter.org', 'http://www.happyfeetpit.com', '1592608983', None, None, 'https://www.hilton.com/en/hotels/msnhwhw-homewood-suites-madison-west/?SEO_id=YELP-HW-MSNHWHW', 'https://www.torrid.com/store-details?StoreID=5119', 'http://www.carpetrepairservices.ca', 'https://WinnerLimo.com', 'http://www.gamestop.com', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2fnc%2fcharlotte%2fpineville-park-rd&sisearchengine=1524&siproduct=2518_Bus', 'https://www.chick-fil-a.com/carolinamall', 'https://stores.loft.com/us/nc/charlotte/4400-sharon-road.html', 'http://www.anthonyvincenailspa.com', 'https://slateratlas.com/lasvegas/', 'https://www.calgarycoop.com/stores/shawnessy/', None, 'https://nobilitea.us/locations/', 'http://www.loveandlearnpreschool.org/', 'http://pandamoniumdoughnuts.wixsite.com/pandamoniumdoughnuts', 'https://tanrepublic.com/locations/nevada/las-vegas/sahara/', None, 'http://www.bk.com', 'http://www.sataymama.com', None, 'https://icencake.com', 'http://www.montelagovillage.com/?mobile=no&cmpid=101520-Yelp', 'http://www.soswildlifecontrol.com/wildlife-removal-toronto/', 'https://petvalu.com/location/3204', 'http://www.brothersbodyshopinc.com', 'http://leslie.jerusalemrestaurant.ca/menus/', 'http://www.bowlbrunswick.com/location/brunswick-zone-mississauga-bowl', None, 'https://www.ulta.com/stores/las-vegas-nv-301', 'http://redwingshoes.com/', 'http://torontobeautyclinic.ca', 'https://www.onceuponachild.com/whitby', None, '1592609108', None, 'http://www.mlkafricanhairbraiding.com', 'http://onehourapplianceandrepair.com/', '1592609123', 'https://www.wyndhamhotels.com/hotel/04734?tel=18003291073&iata=00065402&cid=fe:di:20161220:yl:pp:dius:04734', 'http://www.boxcarsocial.ca/', 'http://www.papajohns.com', 'http://www.escapetocharters.com', 'https://thirteen55motorsports.com', 'http://www.revivemedicalaesthetics.com/', None, 'https://www.redstarvapor.com/stores/vape-shop-phoenix-greenway-rd/', 'http://www.madewell1937.com', None, 'https://canvasnailsandspa.com/book', 'http://www.unitedpoolservice.com/', 'https://www.hertz.com/rentacar/location/unitedstates/arizona/chandler/PHXE02', 'http://laverandaresto.com/', 'http://hytekmed.com', 'http://www.thorindustriesnv.com', None, 'http://www.rossstores.com', 'https://www.bbvacompass.com/USA/AZ/Scottsdale/7155-E-Thunderbird-Rd/', 'https://www.alter8.com', None, 'http://maxmara.com', 'http://www.nizalideo.com', 'http://goodearthcoffeehouse.com', None, 'http://www.babybryan.ca', None, 'http://www.renodepot.com/en/store/reno-depot-aurora', '1592609222', 'https://carolinasnaturalhealth.com', 'http://Avalonnailsspa.com', 'http://hottubscalgary.ca', 'http://www.boboteaandjuice.com', None, 'http://www.chezrobin.com', 'http://wendys.com/', None, 'http://www.ooogoods.com', 'http://www.cafeforte.com', 'http://www.foodlion.com', 'https://www.clubwyndham.com/cw/resorts/orange-tree-golf-resort.page?utm_medium=referral&utm_source=yelp-local&utm_campaign=yext&utm_content=orangetreeresort', None, 'http://dentistslakewoodca.com/', 'http://locations.bannerhealth.com/az/mesa/wound-treatment-mesa-az-bhaz-hclc-91.html', 'https://www.midas.com/phoenix/store.aspx?shopnum=1109&dmanum=684001', 'http://www.harveys.ca', None, 'http://www.costco.com/WarehouseLocatorDetailsView?langId=-1&storeId=10301&catalogId=10701&warehouseNumber=436&BeginAddress=85284&numOfWarehousesToReturn=null&location=85284&callingPage=WarehouseLocatorView', 'http://frillylilly.ca/boutiques/frilly-lilly-mission', '1592609287', None, 'http://www.eversharppowerequipment.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://www.tammywhite.net?cmpid=CQ00_BLM_0006', 'http://www.elementalaesthetics.com/', None, 'http://www.signaturestyle.com/salondetail/default.asp?salonid=38018', 'http://www.mattressfirm.com', 'http://www.gilbertdentalcare.net', 'http://www.acehardware.com/store-details/16053', 'http://www.7-eleven.com/?yelp=29384', None, 'https://www.hashkitchen.com', None, None, 'http://www.indochinewilmington.com/', None, 'http://nhlakesidefamilyphysicians.org', None, None, 'http://www.allabouttimeclockrepair.com', 'http://www.gnc.com', 'http://www.pueblo-mechanical.com', 'http://pulmonarylasvegas.com', 'http://www.findlayvolvocarslv.com', None, 'http://www.crossfitcholla.com', 'http://www.jiveturkeylegs.com', 'http://www.macsindoorgolf.com', 'http://www.estrellafamilymedical.com', 'http://www.libertyvillageaptslasvegas.com/', 'http://www.unitypoint.org', 'http://www.timhortons.com', None, None, 'http://lighthouseflowershopmesa.com/', None, None, 'https://www.cleanslatewaxspa.com', None, 'http://www.lagunaatarrowheadranch.com', 'http://www.jeffbuttsgolf.com/', None, 'https://www.avondalepediatrician.com', None, None, 'https://www.thebrick.com/pages/store-scarborough-eglinton', 'https://www.terroshealth.org', 'https://www.weightwatchers.com/us/find-a-meeting/1215049/ww-studio-park-selwyn-terrace-shopping-center-charlotte-nc', 'http://www.childersandcoventry.com', None, None, 'http://www.grocerymarket.ca', 'http://www.rockowitzortho.com', 'http://www.tangerineasiancuisine.com', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', None, 'http://www.crabbyjoes.com/locations-bradford.php', None, 'http://worldbuffetwi.com', 'http://www.theclayroom.ca', 'http://www.madisonminimarathon.com', 'http://www.nulounge.com', 'http://locations.arbys.com/us/oh/north-royalton/6395-royalton-rd.html', 'https://www.applebees.com/en/restaurants-lyndhurst-oh/5658-mayfield-road-86019', 'http://www.moonvalleynurseries.com', None, None, 'http://www.costco.com', None, 'http://www.foodbasics.ca', 'http://www.stefanssoccer.com', 'http://www.trilliumresidential.com', '1592609535', 'http://sweetfrog.com/locations/store/sweet-frog-white-hall-commons-charlotte-nc', 'https://www.amazinghealingwaters.com', 'http://hmartca.com', 'http://www.pharmasave.com/pharmasave-davisville/9785/mypharmasave.aspx', None, 'http://www.cactusflower.com/ProductDisplay-Local+Delivery-Anniversary.html?srccode=yelp_track', 'http://a1dentalcare.com', 'https://www.zyn.ca', 'https://rsbelectricalinc.com', 'http://www.foxyladylv.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.cirillosacademy.com/', 'http://www.americanvapeandsmoke.com', 'http://www.installturfaz.com', 'http://www.jekproperties.com', 'http://www.oldtowncandyandtoys.com/', 'https://www.moonvalleynurseries.com/locations/northwest-las-vegas?utm_campaign=yelp&utm_source=yelp-nv&utm_medium=rancho', None, 'http://www.francovitiello.com?cmpid=jfqn_blm_0006', 'http://www.aislebound.com', None, None, 'http://www.ae3q.com', 'http://hotel1333.com/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.myvitamintherapy.com', 'http://www.thecorkscrew.com/', 'http://www.desmetautosales.com/', '1592609635', None, 'http://cpllabs.com/', None, None, None, None, 'http://drarthurbenson.com', 'http://www.insurewithtara.com?cmpid=KRBF_BLM_0006', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sushishop.com/fr', 'http://roofriteaz.com', 'http://www.yourmomsdonutsnc.com', None, 'http://www.bevmo.com', 'http://www.customfriction.com/', 'http://www.germansausageaz.com', None, 'http://www.impactptaz.com', 'http://www.pizzaville.ca', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.heroburgers.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLTFS', 'https://corerecoveryaz.com', 'http://www.undertowphx.com', 'http://www.monorchid.com', 'http://www.purenailspasalon.com', 'http://oakmontbakery.com', 'http://activegreenross.com', 'http://www.minaolive.com', 'http://www.montblanc.com', None, 'http://www.anytimeelectriclv.com', 'http://www.phoenixrealestateandhomes.com/phoenix-real-estate-agent-john-cunningham', 'http://www.darlingtennis.com', 'https://www.lowes.com/store/NV-Las-Vegas/1719', 'http://www.starbucks.com/store/15887/', 'http://www.phelpsnursery.com/', 'https://troystreeservice.com', 'http://www.carcollectionnc.com', 'http://www.thirstyscholarpgh.com', None, 'http://xcellencecoolingandheating.com/', None, 'http://acoolbreeze.net', None, None, 'http://www.chachago.ca', 'http://www.publichousegastropub.ca', 'http://www.reflexmedical.net', None, 'http://www.lizharrisrealtor.com', None, 'http://www.phoenixcavaliers.com', 'http://www.carasboutique.com', None, None, 'https://escaperoomvegas.com', 'http://www.coachj.ca/', 'http://crowdsiren.com', None, 'http://www.rmbrow.com', 'http://fountainhillsfamilypractice.com/', 'http://www.usairways.com/en-US/traveltools/club/locations.html#P', None, 'https://www.countrysideanimal.com/?utm_source=yelp&utm_medium=social', 'http://www.mediterrabakehouse.com', 'http://www.cochran.com/', 'http://www.beamhvac.com', 'https://www.cash1loans.com/locations/arizona-stores/title-loans-chandler-az-w-elliot.aspx', 'http://www.themacclinic.com', None, '1592609894', 'http://www.caprijewelersaz.com/', None, 'http://funflick.com/midway/', 'https://adept-garage-doors-north.business.site', 'https://www.brunswickautomartchryslerjeep.com', 'http://azpartybooth.com', None, 'http://www.tgifridays.com', 'https://www.redlobster.com/locations/list/az/gilbert/3845-s-gilbert-road', 'http://www.experttailorlv.com', 'http://www.caretakerlandscape.com/', None, None, None, 'https://twomenandatruck.com/movers/az/phoenix/northwest', None, 'http://travelmed.ca', 'http://www.loucoopey.com', 'http://www.eagletkdlv.com/', '1592609961', 'http://www.azallergy.com', 'https://escaperoomclev.com/escape-room-cleveland/', 'http://azorthopedic.com', '1592609977', None, '1592609986', 'http://www.anylabtestnow.com/franchises/medina-44256/', 'http://www.thedirtybird.ca', 'https://www.squareviewapartments.com', 'http://www.nikkosushibar.net', None, 'https://davidlethcho.business.site', 'https://locations.wendys.com/united-states/az/fountain-hills/17218-e-shea-blvd', 'https://www.knightsinn.com/Mesa-AZ', 'http://www.sourceliquidations.com', 'https://stunnerlab.com', 'http://www.speedway.com', 'http://www.stonewatergolf.com', 'http://scalpskintreatments.com', 'http://www.uCRACKit-iFIXit.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCCF', None, 'http://metalsupermarkets.com/phoenix-southwest/', 'http://arizonarestorationspecialists.com/', 'http://www.tridelco.com', None, None, 'http://www.powerhouseperformanceauto.com', 'http://focusbooth.ca', 'http://www.harborfreight.com', '1592610604', 'http://nervousdog.com/', 'http://www.rosedaledogs.com', 'http://www.movemvp.com', 'https://www.ahn.org/locations/allegheny-general-hospital', 'https://fiestahenderson.sclv.com/?utm_source=YELP&utm_medium=SOCIAL&utm_term=FH&utm_content=FH-PROPERTIES&utm_campaign=FH-YELP', 'https://bikeworldlv.com', None, 'http://machupicchucharlotte.com', None, 'http://www.curves.com', None, 'http://www.cccnevada.com/doctor/john-wojcik-md-fccp-dabsm', 'http://drakegeneralstore.ca', None, 'http://www.marriott.com/hotels/travel/phxox-moxy-phoenix-tempe', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.kelly.com', '1592610670', None, 'http://www.show-us-your-tips.com', 'https://www.chinawokmiddletonwi.com', None, None, None, None, 'http://www.teresaspizza.com', None, 'http://highlandcornergrill.com', 'http://www.caribbeanhvac.us', 'http://albioncinema.com', 'http://www.suitstoyou.com', None, None, 'http://goldenfireacupuncture.com', None, None, 'http://www.susiesmexicancafe.com/', 'http://shawnbensodds.com', 'http://www.davidstroman.com', 'http://www.kannapolisnailsalon.com', None, 'http://www.eccocionline.com', 'http://www.lashandbrowbyvicky.com', 'http://jdsautomotiveshop.com', 'http://www.chaparralanimalspa.com', 'https://www.orthopedicstemcellsscottsdale.com', None, None, 'http://irondrivecoatings.com/', 'https://www.thefastpark.com/airport-parking/cleveland-hopkins-cle-afp', 'https://bayshorehomesales.com', 'http://SalonRootz.com', 'http://www.orangeleafyogurt.com', 'http://www.thecornerplace.ca', 'https://www.minuteloancenter.com/locations/?id=vegas-1', None, 'http://www.acheapbodyshop.com/', None, None, None, None, 'http://www.paragonsecurity.ca', 'https://www.airportautocare.com', 'http://www.mgmgrand.com/meetings/business-center.aspx', 'http://cleostreasures.com', None, 'http://www.mcdonalds.ca', 'https://stores.advanceautoparts.com/pa/pittsburgh/1347-west-liberty-avenue', None, 'https://topgolf.com/us/glendale', 'http://www.nunthapornthai.com', None, 'https://www.uber.com', 'http://www.kylesfastautoglass.com', 'http://www.francisandsonscarwash.com/category/7878/francis-and-sons-car-wash-of-phoenix-az.htm', 'http://www.goodroadciderworks.com', None, 'http://www.greatclips.com/salons/6330', 'http://www.dunkindonuts.com', 'http://www.mrgreek.com', '1592610868', 'http://www.sleepnumber.com/?utm_source=Yelp&utm_medium=CPC&utm_term=CTA&utm_campaign=c8-LvZtDWdCIwUrImw1vtg&cm_mmc=Yelp-_-Yelp-_-WebsiteLink-_-c8-LvZtDWdCIwUrImw1vtg-904825&tag=904825', '1592610872', None, None, None, 'http://guardianinterlock.com/', 'http://www.scotsmanswell.com/', None, 'https://www.davisbrosrefinishing.com/index', None, None, 'http://www.crosstowncarwash.ca', None, 'https://www.blsindia-canada.com', None, 'http://www.desertlakedental.com', 'https://stores.cartier.com/united-states/nv/las-vegas/3131-las-vegas-blvd-south', 'http://www.topfoodil.com', 'https://www.eatnplaycafe.com', 'http://www.americanfineartgallery.com', 'http://www.sherwin-williams.com/store-locator/paint-store/Rock%20Hill/SC/2582', 'http://www.rodgersteam.com', 'http://www.rockhillpediatrics.org/', 'http://www.activsound.com', 'http://www.mlfchildrenstherapy.com', 'https://www.oilerie.com/sun-prairie.html?Affiliate=sun-prairie', 'http://www.destinationxl.com/mens-big-and-tall-store/storelocator/storeDetails.jsp?storeNumber=+9407', None, 'http://www.cepizza.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.townandcountrytoyota.com', 'http://www.talkingstickresort.com/meetingsandevents/meetingsandconferences.aspx', None, 'http://www.tntautoglassnc.com', 'https://rightspacestorage.com/self-storage-locations/arizona/mesa-az-storage-units/6660-E-Main-St', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/109+Dabney+Drive-Henderson-NC-27536/storeid=7055?cid=ps_ylp_2020', None, 'https://bostonpizza.com/en/locations/sunridge.html', None, None, None, 'https://www.firehousesubs.ca', None, 'http://www.lindomichoacanicecream.com', 'http://thewildsidegrill.com/', 'http://www.pizzahut.com/', 'http://dreamdinners.com/main.php?page=store&id=53', 'http://www.gdousjuicychicken.com', 'http://www.412plumbing.com', None, 'http://www.rossstores.com', 'http://www.edgelineflats.com/', 'http://www.fppaz.com', 'http://www.tazhair.com/', 'http://eggspectation.com/locations/canada/longueuil/', None, 'http://www.lelandsbarbershop.com', None, 'http://www.wildbunchcatering.com', 'http://shop.exclucitylife.com', 'https://stores.joann.com/az/phoenix/1917/', '1592611001', None, 'http://redcarpetplumbing.com', None, None, 'http://www.modernfamilydentalcare.com/', 'https://locations.wendys.com/canada/on/markham/9970-highway-48', None, None, 'https://jewelrybuyersonline.com', 'http://drstephenfry.com', None, 'http://www.snorthodontics.com', None, 'http://ideal-laundromat.business.site', 'http://www.thekiltedbuffalo.com', 'https://www.napaautopro.com/auto-repair/alberta/calgary-impressions-automotive-ltd/', None, None, 'http://lasvegas.jiffylube.com/Locations/Store/1975/4531-N-RANCHO-RD-LAS-VEGAS-NV-89130-3403', None, 'http://www.offthewallarttoronto.com', None, None, 'http://www.capcentremarket.com/', 'http://rsheabrewing.com', 'http://www.jessicalloydbeauty.com', 'http://www.secondcup.com', None, 'http://locations.michaels.com/az/mesa/2778/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', None, 'http://www.quesada.ca', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.gianteagle.com', '1592611079', None, 'http://www.tqla.com', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', '1592611092', None, 'http://www.ponchosmexicanfood.com', 'http://www.waldhorn.us/', 'http://www.fatlambkouzina.com', None, 'https://www.crossroadshospice.com/locations/ohio/valley-view-oh/', 'http://www.donaldsonwatchrepair.com', 'http://fuelpizza.com', 'http://www.la-z-boy.com/Toronto/Highway-7-East/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/118+West+Garfield+Street-Aurora-OH-44202/storeid=3393?cid=ps_ylp_2020', None, 'http://www.candhroofinginc.com/', None, None, None, 'http://www.starbucks.com/', 'http://www.debearjjewellers.ca', 'https://morristrust.com', 'http://www.noda101.com', 'http://mullinstrenchak.com', 'https://www.maaco.com/locations/nv/las-vegas-12597/?utm_medium=bry&utm_source=yellowpages&utm_campaign=m2597', None, None, 'http://www.impmesa.com', 'http://www.duckrabbitcoffee.com', None, 'https://alberta.weidner.com/apartments/ab/calgary/3600-brentwood/', None, 'http://WhitmoresBBQ.com', '1592611163', None, 'https://peabodyconstlv.com', 'https://us.megabus.com/?utm_source=Yelp&utm_medium=Yelp&utm_campaign=Pittsburgh%20Page', None, 'http://www.storkvisionaz.com', 'http://www.abellpestcontrol.com', 'http://www.merelash.com', None, None, 'http://www.ecoorganicspa.com', 'http://www.mainstreetcupcakes.com/', 'http://madisonbetterbody.massagetherapy.com/', 'http://www.metcentre.com/', None, None, 'http://www.act4u.com/schools/MStarkanian.html', None, None, 'http://www.cannibale.ca/', '1592611209', 'https://www.davidsbridal.com/?utm_source=Yelp&utm_medium=OrganicSearch&utm_term=74&utm_content=DisplayURL&utm_campaign=WebsiteListing', 'http://foothillsacademy.com/', 'https://www.morfurniture.com/store/gilbert', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280205718&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://locations.bojangles.com/nc/waxhaw/2933-providence-road-south.html', '1592611227', 'http://activerunnerstrongsville.com/site/', 'https://locations.davidstea.com/on-toronto-1', 'http://www.acac.net/', 'http://www.thelexoncentral.com', None, 'http://www.scratchoff.com', 'http://www.theclutterhouse.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.favillephoto.com', 'http://sparklesbeautybars.com', 'http://sergiopenha.com', 'http://solarsafepoolcovers.com', None, 'https://www.viscontiatcamelback.com', 'https://aires.com/', 'https://planetgeekllc.com', 'http://coffeycanfixit.com', 'http://www.leftyslv.com', 'https://megafurnitureusa.com', '1592611277', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3034+West+Lincoln+Avenue-Peoria-IL-61604/storeid=7798?cid=ps_ylp_2020', 'https://www.ilovekickboxing.com/studio/index.php?id=607', 'http://www.jerseyboysinfo.com/vegas/contact.html', None, 'http://www.jusubar.com', 'http://www.grayhawkortho.com', 'http://www.babushkafoods.com', None, None, 'http://www.dreamsdc.ca', 'http://www.winners.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.donaldpark.org/', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Cornelius-NC-28031/780027/', 'http://twiceup.food46.com', 'http://www.plumbernv.com', 'https://www.wellsfargo.com', '1592611321', 'http://www.brainbalancecenters.com?=yelp_track', 'http://lucynails-toronto.business.site', 'http://simplyconstruction.net', 'http://www.valleybrows.com', 'http://www.balllawfirm.com/', 'http://www.coppacoffeeandtea.com', 'http://www.deerfootmeadows.com/', 'http://www.peninsulayacht.com', 'http://www.mcmathrealty.com/', None, 'http://twobrothersbrewing.com/restaurants/scottsdale-tap-house-and-brewery/', 'http://www.pioneersand.com', 'https://campbellssweets.com/locations/campbells-sweets-factory-ohio-city/', None, 'http://www.gymboreeclasses.com/lknnc.site', 'http://www.spritzjewelers.com', 'http://www.freehdtvaz.com', 'http://healingchirohands.com/', None, 'http://www.hcpnv.com/providers/prashantdani/', 'http://www.arizonastoragecenters.com/Glendale-Cactus-Self-Storage', '1592611375', 'https://www.ginospizza.ca', 'http://www.lawntechohio.com', None, 'http://antechhair.com', None, 'http://longwongsoflaveen.com/', None, None, 'http://www.aawgallery.com', None, None, 'http://www.growlandllc.com/', None, 'http://www.teriyakiexperience.com/en/home.html', 'http://www.zendogservices.com', None, 'http://www.precisiontune.com/CharlotteNC_NorthTryonSt', None, 'http://www.lawnmaintenanceintempeaz.com', None, 'http://www.waxon.ca', 'http://www.ljsilvers.com/', None, 'http://www.surplusfurniture.com/en/calgary-south/', 'http://dawsondental.ca/our-locations/toronto-dentist-yorkville', 'http://torontopopcorncompany.com', 'http://www.trinitymedicalimaging.ca', 'https://upfreshkitchen.com', 'https://brusters.com/IngomarPa', None, 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, 'http://rjglassaz.com', 'http://strategygames.ca', 'http://www.peaceloveandhairsalon.com', 'https://www.athleticareonline.com', 'http://www.totalhealthbc.com/', 'http://therealestateguylv.com', None, 'http://www.overtimesportsgrilleaz.com', 'http://UrsulasPianoStudio.com', 'http://www.cafeplenty.com/', None, None, 'http://prestoautoloans.com', 'http://www.tropicalsmoothiecafe.com', None, None, 'http://www.bk.com', 'http://labohemecafe.ca/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3034+West+Lincoln+Avenue-Peoria-IL-61604/storeid=7798?cid=ps_ylp_2020', 'https://www.lvchinatownplaza.com', 'http://www.bcbg.com', None, 'https://locations.captainds.com/ll/US/NC/Charlotte/2838-Freedom-Dr', 'http://scottsdalescubadiving.com', 'https://www.agperfection.com', 'http://centrestreetpub.ca', 'http://www.shedrawsyou.com', 'http://www.goodsamcan.com', '1592611520', '1592611523', 'http://www.nevadasouthern.com', 'http://www.vitaminon.com', None, 'http://www.acrmasterlocksmith.com', 'http://www.cielosalonandspa.com/', 'https://atomicstylelounge.com', 'http://www.oldeavonvillage.com/treehouse.htm', 'http://www.fourseasons.com/scottsdale/spa.html', None, None, 'http://www.crossfitunwavering.com', 'http://bloomrestaurant.com/', 'http://underparindoorgolf.com', None, 'http://www.cobalthairapothecary.com', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=14', 'https://yournewbreastfriend.com', '1592611566', '1592611569', '1592611572', 'http://www.dilworthcustomframing.com', None, None, None, None, None, None, None, '1592611593', 'http://www.brightindependentvolvo.com', 'http://www.karakahl.com', 'http://www.northeastfactorydirect.com', 'http://vistanciaortho.com', None, 'http://www.salonnaman.com', None, 'http://cell-doc.com/locations/iphone-repair-north-olmsted-oh/', 'http://edisoncleaners.com', None, None, 'https://www.walgreens.com/locator/walgreens-1159+e+southern+ave-mesa-az-85204/id=3670', 'https://www.enterprise.com/en/car-rental/locations/us/oh/warrensville-heights-3976.html?mcid=iyp:8368400', None, None, None, 'https://mountainsidefitness.com/locations/scottsdale-shea/', 'http://www.eudyscabinets.com', None, 'http://www.image360.com/lasvegassouthnv', 'http://oasisbagels.com/', 'http://www.mytatumdentalcare.com/', '1592611643', 'http://www.freshhaironline.com', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', None, 'http://www.impactdj.ca/', None, 'http://www.prestocafelv.com/', 'http://www.venetian.com/GCS.aspx', None, None, 'https://www.energyonewindows.com', 'https://www.containerstore.com/locations/showStore.htm?store=CLE', 'http://asiancuisinemonroeville.com/', None, 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'http://lvlevictions.com', 'https://fiestarancho.sclv.com/Dining/Festival-Buffet', None, None, 'http://www.timothyscafes.com', None, 'http://www.gunforall.com/', 'http://blossomspa.co', 'http://royalspringshc.com', 'http://www.opticgallerysahara.com', 'http://www.bristoltruckrentals.com/locations/brampton-trucks', 'https://kiwanismarketplace.org', 'https://www.wildwingrestaurants.com', '1592611713', 'http://lgnailspa.com/', '1592611719', 'http://www.stevemadden.com/custserv/store_details.jsp?storeId=1005', 'http://www.tnt-supermarket.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://fiestarancho.sclv.com/Gaming/Bingo', None, 'http://www.scooters.ca/', 'http://www.phils.ca', 'http://www.freshcityfarms.com', 'http://littleburgundyshoes.com', 'https://www.usdermatologypartners.com/north-valley-dermatology-peoria/', 'http://www.steppingstonesacademy.org', 'http://www.clevelandcamerarental.com', '1592611753', 'http://www.relaxtheback.com/stores/pittsburgh-east-liberty', 'http://hillcrestfamilyvision.com', 'http://www.myrosatis.com/store-details/Mesa%20Greenfield', None, 'https://www.theshowerdoorstore.ca', 'http://www.tipsnailbar.ca', None, 'http://www.FreddiesNutrition.com', 'http://www.eyeopia.com', None, None, 'http://www.gong-cha.ca', 'http://voulezvouscafe.com/', 'http://www.skyloftsmgmgrand.com', 'http://preciousbeauty.yolasite.com', 'http://www.bensonbingham.com', 'http://www.insuremejulie.com?cmpid=fgbx_blm_0006', None, 'http://www.piazzamonte.com', None, 'http://www.carters.com/home?id=carters&cm_mmc=Retail-_-Carters-_-Yelp-_-April', 'http://www.madamethai.ca', 'http://www.greatclips.com/', 'http://www.twelvepgh.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/oh/cleveland-shaker-heights-3970.html?mcid=iyp:8368400', 'http://baydentaloffice.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.walgreens.com/locator/walgreens-5300+monona+dr-monona-wi-53716/id=4830', 'http://www.woodiesautoservice.com', 'http://www.kay.com', None, 'http://phx1.org', None, 'http://www.vocellipizza.com/ambridge_pa', 'https://www.americancampus.com/student-apartments/nc/charlotte/university-walk', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'http://www.walkinurgentcare.com', 'http://www.autorehab.repair', 'http://www.lashingoutonmain.com', None, None, None, 'https://elevationchurch.org/locations/matthews/', None, 'http://www.brimleylawrenceanimalclinic.ca', '1592611855', 'https://www.belk.com/shop-by-brand/benefit-cosmetics/benefit-brow-bar/', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1850+West+Franklin+Boulevard-Gastonia-NC-28052/storeid=3823?cid=ps_ylp_2020', 'http://www.tangswok.com', 'http://www.finessepermanentmakeup.com/', 'http://www.asu.edu/tour/west/vrde.html', 'http://www.midnightdinercharlotte.com/', 'http://www.buzzboyzbarbershop.com/', None, None, 'http://www.universalfordlincoln.com', None, 'http://www.annabellebridal.com', 'http://deercreekah.net', 'http://bikeoh.com', None, None, None, 'http://www.theappliancewarehouse.ca', None, 'www.quakersteakandlube.com/', 'https://www.lvspartanpools.com', None, 'http://tricitycardiology.com', 'http://www.standuplive.com', None, None, None, 'https://agents.allstate.com/don-stoll-tempe-az/auto-insurance.html', 'http://premierlandscapemaintenance.webnode.com/', None, 'http://www.azjawdoc.com/home', None, None, 'http://www.skinbydesign.ca/', 'http://www.evelinecharles.com', 'http://eddysbarbershop.com/west/#barbers', 'http://www.7-eleven.com/?yelp=22886', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://clovenc.com', 'http://www.alleen.com', 'http://www.dunkindonuts.com', None, 'http://www.gamestop.com', None, 'http://dufferinmalldental.com', 'http://www.jiffylube.com', 'http://www.theredlighttoronto.com', 'http://www.bodyheattanning.com', 'http://globalbazaar.ca', 'http://www.cananphotography.com', 'http://www.jiffylube.com', 'https://www.gowireless.com/stores/az/phoenix/phoenix-ahwatukee-foothills/', 'http://local.biglots.com/az/phoenix/4085', 'http://www.dapizzeria.com/', None, 'http://www.safariairlasvegas.com', 'http://montreal.breakoutescapegame.com/fr', 'http://www.violinslover.com', None, None, None, 'http://www.doorcreekorchard.com', None, 'http://www.asinglemomcleaning.wixsite.com/mysite', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'https://www.plannedparenthood.org/health-center/arizona/chandler/85224/chandler-health-center-2812-90030?utm_campaign=chandler-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', 'http://www.melangeconsignment.com', None, 'http://www.whereonearth.ca', None, 'http://www.thebiermarkt.com', 'https://www.buffaloexchange.com/locations/phoenix/tempe/', 'http://ValienteMott.com', 'http://therabbitspot.com/the-rabbit-hole/', 'http://10thplanetdtlv.com', 'https://www.cyclopediato.com', None, '1592655893', 'https://www.codeninjas.com/locations/nv-summerlin', 'http://www.iticket.law', None, None, 'http://ransombayinn-vt.com', None, 'http://www.sokolowskis.com', None, 'http://cakesbyrobert.com/', 'http://airconditioningeastvalley.com', None, None, 'https://www.nofrills.ca/store-locator/Chris%27+nofrills+%28Renforth+Dr.%29/0273?storeId=0273', '1592655918', None, 'https://torontoscubacentre.com', 'http://www.papamurphys.com/', None, 'http://www.lotusrainhealing.com', None, 'http://www.theogvegas.com', 'http://www.terribleherbst.com/', 'https://www.amilispizzahp.com', 'http://azturfsolutions.com/', None, None, 'http://www.misterfrenchy.com', None, 'https://www.wellsfargo.com', 'http://www.dunhamssports.com/stores/sporting-goods-monroeville-pa/', 'http://www.skyviewbanquets.com', 'http://www.mrsandwichlv.com/', 'http://www.aquapiranhapools.com', None, 'http://www.thefurnitureranch.com/', 'http://www.extremepita.com/', 'http://www.dinerscorner.com', '1592655974', 'http://www.papajohns.com', None, None, None, 'http://www.themakerbean.com', 'http://www.thejunctionbeveragedrivethru.com', 'http://www.burnbootcamp.com/tega-cay-sc', 'http://www.circlek.com', None, 'http://www.marcos.com/locations/oh/north-olmsted/lorain-rd?s=true', '1592655996', 'https://www.serpentini-tallmadge.com', None, 'http://www.falloutgames.net', '1592656005', 'https://www.cricketwireless.com', None, 'https://lockguyz.com', 'http://parkingticketguys.com', None, None, 'http://www.kindskintherapy.com', 'http://www.d2ehairboutique.com', 'http://www.carefreecarpet.com', 'http://www.redrockwealth.com', 'http://locations.rentacenter.com/arizona/phoenix/85016/2341-e-indian-school-rd/', None, None, 'http://500move.com', 'http://www.phobosabistro.com', None, None, 'http://www.baanthaimassage.ca/', 'http://nails-time.com', None, '1592656051', None, 'http://foodtohomes.com', 'http://www.tesla.com', 'https://haircutmennorthhillspa.com', 'http://www.hudsonsrestaurant.com', None, 'http://theinsanitea.com', 'http://boulevardmall.com/boulevard-magic-show-dixie-dooley/', 'http://www.cheesegarden.ca', 'http://www.northscottsdalepodiatry.com', 'http://www.xplore-scuba.com', 'http://www.bigfootgaragecabinets.com', 'https://caminorealmiddleton.com', 'http://live1015phoenix.cbslocal.com', None, 'http://www.foothillsrehab.com/', 'http://www.alfierifuneralhome.com', None, None, 'http://www.sandhillpetclinic.com', 'https://www.interdent.com/gentle-dental/locations/az/phoenix/3414-w-union-hills-dr-dentist-office?utm_source=organic&utm_medium=yext', None, None, None, '1592656109', 'http://www.RoyalSalonAZ.com', None, 'http://www.zenithautocare.net', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://www.steaknshake.com/locations/24367-steak-n-shake-s-neil-street-champaign', '1592656127', 'http://www.108noblefootspa.com', None, 'http://www.pioneertitleagency.com', None, 'http://www.blackstrapbbq.ca', 'http://www.goldsgym.com', '1592656144', None, None, None, 'http://www.hottopic.com', 'http://www.masterviolinshop.com', 'https://www.aokairconditioningandrefrigerationllc.com', 'https://pilotflyingj.com/stores/459', 'http://avis.com', 'http://www.bestglass.com', None, 'http://lasvegas.jiffylube.com/Locations/Store/1975/4531-N-RANCHO-RD-LAS-VEGAS-NV-89130-3403', 'http://www.willowdalesubaru.com', None, None, 'http://www.goldfingerslasvegas.com', 'http://www.posaresalons.com', 'http://www.papanickspizzacleveland.com', 'https://www.irepairplus.com', None, None, 'http://www.cuskicplumbing.com/index.html', 'http://www.marshallstearns.com', None, None, 'https://fullypromoted.com/locations/cleveland-west-oh/', 'http://www.zaikabiryanihouse.com', 'http://www.americanroyalpalace.com', 'https://stores.petco.com/az/mesa/pet-supplies-mesa-az-1119.html', 'https://www.wyndhamhotels.com/hotel/48959?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:48959', None, 'http://chalaudimsum.com', 'http://www.wholesalesuppliesplus.com/', 'https://www.storagewest.com/facilities/buffalo-drive/?utm_medium=organic&utm_campaign=yext&utm_source=yelp', 'http://www.beauvisagespa.com', 'http://www.gravitysportslv.com', 'http://freshandeasy.com', None, 'http://www.fieldwork.com', 'http://www.abcrentalparma.com', None, 'https://www.hazzevape.com', 'http://www.industrialshoecompany.com', None, 'http://www.babiesrus.com', 'http://www.bizzyb.ca', 'http://drummondcarpetcleaner.com', 'http://www.unioncab.com', 'https://stores.advanceautoparts.com/oh/strongsville/14206-pearl-rd?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7784&localechange=1', 'https://www.aircanada.com/ca/fr/aco/home/fly/premium-services/maple-leaf-lounges.html', 'http://www.thebarlv.com', None, 'http://coolvybz-jamaican-restaurant.business.site', 'http://www.starbucks.com/store/9229/', '1592656266', 'http://www.fye.com', 'http://naturalbeautyaz.com', None, None, 'https://www.truerest.com/locations/wexford/', None, 'http://www.hairstudiodayspa.com', 'https://thefoot.grouppayless.com', 'http://dspotdessert.com', 'https://www.e-zrentacar.com/location/toronto-pearson-international-airport-yyz/', 'http://trustarts.culturaldistrict.org/production/47098/the-chocolate-bar-at-the-benedum-center', None, 'https://kruppmoving.com', None, 'https://www.sushitaxi.net/fr/succursales/saint-sauveur', '1592656303', None, None, 'http://eatatmenus.com', 'http://www.afinebikiniline.com/', 'http://justsushi.com', 'http://azurogyn.com/', 'http://www.mesawaterandice.com/', None, None, 'http://www.littlecaesars.com', None, None, 'http://www.banfield.com/veterinarians/nc/charlotte/bky?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.pizzadelarte.ca', 'http://www.dignitymemorial.com/funeral-homes/henderson-nv/palm-boulder-highway-mortuary-and-cemetery/1010', 'https://smile-dessert.business.site', 'http://www.mecklenburgmedicalgroup.org', 'https://www.bluemercury.com/pages/store-details?store_number=172134', 'https://www.usabmx.com/tracks/0001', None, 'http://www.purerelaxmassage.com', None, None, 'http://vandvautorepair.com', None, '1592656359', 'http://www.timhortons.com', 'https://www.tacobell.com/food?utm_source=yelp&utm_medium=social&utm_campaign=yelp-pilot-test-menu-static-1-CS&utm_content=paid', 'http://www.yogaloft.ca/', None, 'http://mrgreek.com/morningside', 'http://www.wholefoodsmarket.com/stores/paradisevalley', 'http://www.gracetoronto.ca', 'http://www.verizonwireless.com/stores/nevada/las-vegas/katie-203158/', None, None, None, 'http://www.freshchefkitchen.com', None, 'http://www.makimono.ca/menu/airport/airport.html', 'https://sanomedclinic.ca', None, 'http://www.surpriseaz.gov/index.aspx?NID=229', None, 'http://www.yourlasvegasguide.com', 'http://qualitypaintingaz.com', 'https://www.ticketbat.com/event/cameo', 'http://palms.com/casino.html?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://potofgoldestate.com', '1592656414', None, None, 'http://www.vcahospitals.com/northern/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Northern_Animal_Hospital&utm_campaign=main_url', None, None, 'http://microsoft.com/en-us/store/locations/nv/las-vegas/fashion-show/store-1025?pointit_retailsustain_sitelinks_Yelp', None, None, 'http://oasissurf.com/', 'http://www.drivingclass.com', 'http://www.justtintit.com', 'http://www.UndergroundFitnessAZ.com', 'http://lasvegasrealtyspecialists.com', None, None, 'http://www.hopsonline.com', 'http://www.projectionboothcinema.com', 'http://www.clevelandcremation.com', None, 'http://www.arizonaoms.com', 'http://www.shopsquareone.com', 'http://www.sleepcountry.ca', 'http://thestockroominc.com/', 'http://www.twinsburgvet.com/', 'http://www.divinemine.com/', 'http://milkys.ca', 'https://www.calgarycoop.com/stores/shawnessy/', 'http://www.echocoffee.com/', 'http://www.breyerlaw.com/office-mesa.html', 'https://www.mainstreetbakehouse.com', 'http://www.tuxedojunction.com', 'http://www.MatchaLV.com', 'http://superpub.ca', 'https://damngoodnachos.com', 'https://www.3brotherspaversllc.com', None, 'http://www.tiretactics.com', None, 'http://www.workshopmb.com', None, 'http://www.toronto.ca/parks/featured-parks/music-garden/', 'http://www.menswearhouse.com', 'https://www.walgreens.com/locator/walgreens-9400+mentor+ave-mentor-oh-44060/id=4317', 'http://www.tlcpcsolutions.com', None, None, 'http://www.valleymetro.org/metrolightrail', None, 'http://www.acmepestcontrolcompany.com', None, 'http://www.wigsbycc.com', None, None, '1592656535', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.brightnow.com', None, 'http://www.theonebridal.ca', 'http://www.VLpartybus.com', None, None, 'https://www.walgreens.com/locator/walgreens-25524+center+ridge+rd-westlake-oh-44145/id=5473', 'http://www.sprint.com', 'https://no900.com/restaurants/centropolis-laval/', 'http://www.raccoonhillgolfclub.com', None, 'http://www.infusedclt.com', 'http://vnaccountingsolutions.com/', 'https://crumblcookies.com', None, 'https://stores.guitarcenter.com/mesa-lessons?source=4GOA5AJBB', None, None, 'http://www.truefittandhill.ca/', None, None, 'http://www.northernmaverick.ca', None, 'http://www.wbypest.com', None, 'http://www.midas.com/pittsburgh/store.aspx?shopnum=6394&dmanum=688', 'http://www.texasroadhouse.com/restaurant-locations/ohio/elyria', 'http://www.Tressformationsalonspa.com', None, 'https://www.bmfclothingandgear.com', 'http://www.yogablissakron.com', 'http://www.cu-needleworks.com/', 'https://bargainstorage.com/arizona/self-storage-phoenix-az/85013-self-storage/608', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.toyosumarkham.com', 'https://locations.wendys.com/united-states/oh/cleveland/13939-euclid-ave.', 'http://www.ambiancehairandnailgallery.com/', None, 'http://www.goldenspoon.com', None, 'http://www.circleatsouthend.com/', None, None, None, 'http://eatatovereasy.com', 'http://www.kidsdentalcenter.com', 'https://www.jeancoutu.com/localisateur-succursale/saint-laurent-802-boulevard-decarie-h4l-3l9/7/', None, 'https://locations.churchs.com/az-phoenix-7235', '1592656649', None, '1592656654', 'http://www.goodfellasbl.com', None, None, 'http://local.firestonecompleteautocare.com/arizona/glendale/3540-w-bell-rd/?lw_cmp=IYP_YPC_MLP_11940', None, 'http://www.paddleboardaddict.com', 'http://sottovoce.ca', None, 'http://www.carguysofscottsdale.com/', None, 'http://VlineElectrical.com', 'http://www.starbucks.com/store/15887/', None, None, 'http://azbeachbikes.com', 'http://www.commandocleaningservice.com', None, None, 'http://www.swurologic.com/', 'http://chapatiindiangrill.com', 'http://www.papajohns.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.northway.org/campus/wexford-campus', 'http://anthonysmenssalon.com', 'http://tomsrestaurant.ca', 'http://www.henrythetailor.com', 'http://www.rustichills.com', 'http://escapesalonandspas.com', '1592657541', 'https://www.agelessforever.net', 'http://www.panerabread.com/', 'http://www.yogisgrill.net', 'https://www.ihg.com/spnd/hotels/us/en/pittsburgh/pitsu/hoteldetail', None, 'http://www.scarehouse.com', 'http://www.JimmyJohns.com', None, '1592657568', 'http://www.century-apartments.com/century-springfield-meadows-fort-mill-sc/', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', '1592657578', 'http://www.goldvampire.com', 'http://titleboxingclubpromotions.com/ohio/', 'http://searsucker.com/las-vegas', None, 'http://spiritsbarandgrill.com', 'http://www.santokibbq.com', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB097', None, 'http://www.krownlakeshore.com/', None, None, None, 'http://www.rvcrcarolina.com', 'http://www.learntosew.ca', 'http://www.mtnviewpestcontrol.com', 'http://www.phxpublicmarket.com', 'http://www.furryfamilyphotos.com', None, 'http://www.candlelightandmemories.com/', None, 'http://www.phoenixacinc.com/', 'http://www.ClearskinInstitute.com', 'http://www.allmobilematters.com/stores/tempe-marketplace/', None, 'http://www.hotboxsalon.com', 'https://sweetthangsbakery.com', 'http://thegroceryoutlet.ca', 'http://www.crawfordappliances.ca', None, None, 'http://modernpets.net/', 'http://www.southhillspoweryoga.com', None, None, None, 'http://www.shorecenterlaundry.com', 'https://www.britishgrocerwholesale.com/', 'http://www.structube.com', None, None, 'http://www.quesada.ca', None, 'http://www.corsicanapts.com', 'http://www.stardustbuilding.org', 'http://www.anthonyamatosalon.com', 'http://www.thorncliffeauto.com', 'http://www.beinspiredsalon.com/home.aspx', 'http://www.riolasvegas.com/restaurants/kj-dim-sum-and-seafood.html', None, 'http://www.cocolezzone.com', 'http://www.azenviroclean.com', 'http://www.snapfitness.com/lasvegas6', None, 'http://www.EveryKidsDentist.com/?sc_cid=Yelp_Listing', 'https://www.discounttire.com/store/az/tempe/s/1007?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'https://locations.postnet.com/az/scottsdale/10869-n-scottsdale-rd', 'http://www.dominos.com', 'http://www.merakisupplyco.com', 'http://www.maccosmetics.com', 'http://www.12-westmain.com', None, 'https://bishops.co/locations/willo/', 'http://www.barbershoplasvegas.com', 'http://www.cntower.ca', None, 'http://www.gelatodimilano.com', None, 'http://www.bi-lo.com', None, 'http://www.bedbathandbeyond.com', 'https://www.zimbrickhyundaiwest.com', 'http://blueorthodontics.com', 'http://www.restobarjulianos.com', 'https://locations.jackinthebox.com/us/az/litchfield-park/13860-w-camelback-rd', 'http://substationaz.com', 'http://www.enricos-pizza.com', None, None, None, 'http://www.stmarknc.org', 'http://www.hakkasanlv.com', 'http://www.dunkindonuts.com', 'http://Charlotte.ArmstrongRelocation.com', 'http://www.vlineclinic.com', None, 'http://www.lashedbyamy.com', 'http://americanbackyardsaz.com', 'http://www.greateventsrentals.ca/', 'http://www.vendettissalon.com', 'https://www.ucedaschool.edu/schools/nevada/las-vegas-ii', '1592657846', None, None, 'http://www.starbucks.com/store/14887/', 'http://www.thompsonmovingllc.com', '1592657854', '1592657857', 'https://www.palms.com/eat-and-drink/saras/', 'http://www.prestigepools.ca/contactus.htm', 'http://pittsburgh.pirates.mlb.com', None, 'http://williamscoffeeco.com', 'https://experimax.com/locations/east-gilbert-az/', 'http://www.murphylifecoaching.com', None, 'http://www.hotelwelcominns.com', None, 'http://www.queencompactcars.com', 'http://www.pizzanopizza.ca', 'http://www.aroma-cafe.com', 'http://www.tanlasvegasonline.com', 'https://www.druryhotels.com/locations/Charlotte-NC/Drury-Inn-and-Suites-Charlotte-Northlake', '1592657893', None, 'http://www.nvsmokeshoponline.com', '1592657900', 'http://www.myperfectskinclinic.com', None, 'http://www.flowersbyterry.com/', 'https://www.barlouie.com/locations/us/wi/glendale/bayshore-town-center?utm_source=other&utm_medium=listings', 'https://www.chilis.com', 'https://twopeasinapodphotography.myportfolio.com', 'http://www.vacuumcleanersmadison.com', None, None, 'https://www.wyndhamhotels.com/hotels/48892?tel=18885959874&iata=00065402&cid=fe:gn:20160201:yl:pp:gn:48892', None, None, None, 'http://www.casacarbone.ca', 'https://www.jerseymikes.com/29011', 'http://cornedbeefhouse.com', 'https://www.lovesac.com', None, '1592657943', 'https://www.goodyearautoservice.com/en-US/shop/OH/Strongsville/000900558-44136', 'http://www.applianceemtexperts.com', 'http://www.azian.ca', 'http://www.kfc.ca/store/1-10-jacob-keffer-pky-maple', 'http://www.infinityhospicecare.com', None, None, 'http://www.harryrosen.com/store/Bloor%20Street', None, None, None, 'http://www.eldoradoanimalhospital.com', 'http://www.DRIOLasVegas.com', 'http://www.jasminegrill.com', None, 'http://www.autocarenc.com', 'http://www.cosmopolitanlasvegas.com/experience/lounges-and-bars/', None, None, 'http://www.thenannyconcierge.com', 'https://texasstation.sclv.com/Dining/Oyster-Bar?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'https://www.pruittsplumbingllc.com', 'https://www.applebees.com/en/restaurants-pineville-nc/10921-carolina-place-parkway-86071', 'http://pivonkahealth.com', 'http://www.pro-filemarketing.com', None, None, 'http://www.vavoomlasvegas.com/', None, 'https://www.dinopalmierisalon.com/locations/rush-by-dino-palmieri/', 'http://LasVegasFirearmsTraining.com', None, None, '1592658023', 'http://www.sonobjj.com', None, 'http://www.mississaugaanimalhospital.ca/', 'http://www.royalpaan.com/store-mississauga-dream-crest.html', 'http://ardentpest.com', 'http://www.crossfit2serve.com', 'http://www.valleyymca.org', 'http://mtnroadcycles.com/storelocator/berea-oh-3.htm', 'http://www.thecountygeneral.ca/', 'http://shearimage.ca', 'http://urmanent.com/', 'http://www.katybugfaye.com', 'http://www.happydentallv.com', 'http://www.iwcohio.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.stronghearttattoo.com/', 'https://www.horwitzvisioncenter.com', 'https://www.sinclairoil.com', 'http://spencerstv.com', 'http://www.planetfitness.com/gyms/charlotte-whitehall-nc-125?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', '1592658072', None, None, 'http://bit.ly/3aqlmiO', '1592658082', None, 'http://www.alimas.ca/', 'http://www.greenbamboodelivery.com/', None, 'http://www.shell.us', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://legacyfitnessaz.com', None, None, 'http://www.sohosalon.ca', None, 'http://www.gammasports.com', 'https://local.safeway.com/safeway/az/scottsdale/23565-n-scottsdale-rd.html', 'https://numberoneescaperoom.com', None, None, None, 'http://www.beguiling.ca', 'http://iwok88.com', 'http://www.gnc.com', 'https://www.grabbagreen.com/stores/healthy-food-scottsdale/34099', 'http://www.glendaledentalgroup-az.com', None, 'http://www.geico.com/insurance-agents/nevada/las-vegas/dean-collotta/', None, 'http://www.mystylistandisea.com/book-online', 'https://horizoneye.com', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'http://www.furnituremaster.ca', 'http://www.kw.com', 'http://www.fadascooters.com/', 'http://www.artsncraftspgh.com', None, 'http://www.cellcirclerepair.com', None, 'http://clicks.dbm-media.com/Yelp_mobile', 'https://sprinkles.com/locations/nv/las-vegas?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.popularpizza.ca/', 'https://www.walgreens.com/locator/walgreens-2010+branch+st-middleton-wi-53562/id=10555', 'https://www.chick-fil-a.com/arboretum', 'http://www.psychiceyeofchase.com', '1592658183', 'http://www.charmeck.org/mecklenburg/county/ParkandRec/Greenways/OpenGreenways/Pages/MallardCreekandClark%27sCreek.aspx', '1592658188', 'http://www.7-eleven.com/?yelp=29384', None, 'https://www.thecoopcowork.com', 'http://www.ballantynedentistry.com', '1592658199', 'http://www.nybutcher.com/', 'http://www.thairedorchid.com', 'http://www.kensingtonliquorcellar.com', 'http://bpiinsulationmadison.com', 'http://www.ihg.com/holidayinn/hotels/us/en/calgary/yycmc/hoteldetail', None, None, 'http://www.1-plus.com', 'http://www.cafezojo.com', 'http://Flamepersiangrill.com', None, 'http://www.sallysoptical.com/home.html', 'https://www.walgreens.com/locator/walgreens-2363+s+lindsay+rd-gilbert-az-85295/id=5215', 'http://local.tiresplus.com/store/Madison-East?lw_cmp=YLP_TP_53714&utm_source=YLP&utm_medium=TP_53714', None, None, None, 'http://avalon.edu/locations/phoenix-az/', 'https://mitchellshomemade.com/shop-updates', 'http://jeffsautocare.com/', None, None, None, '1592658250', None, 'http://www.joesautoaz.com', 'http://www.stjohnsmusic.com/locations/toronto', None, 'http://www.chevron.com', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.tqtire.com/local/Home/NC/Charlotte/1204', 'https://topgolf.com/us/gilbert/', 'http://www.josephineskaught.com', 'https://www.smithsfoodanddrug.com/stores/details/706/00370', '1592658277', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.stlc.com', 'http://sidsavittod.com', 'http://beautifulbridesmadison.com/', 'http://www.Lovemycolon.com', 'http://www.sunrisekidsdental.com', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.tdcanadatrust.com', 'http://www.masterbarbershop.net', 'http://www.zapposinsights.com/tours', 'http://inlinebusinessadvisors.com/', 'http://www.flypittsburgh.com/dine-shop-enjoy/detail?id=7', 'http://www.goldcoastcasino.com/dine/cornerstone?disid=wmm_yelp_gc_corporate_cornerstone_organiclink', 'http://becktaxworks.com', None, None, 'https://www.rfpie.com', '1592658322', '1592658324', 'http://skyhavenlv.com/home/3208667', None, 'https://www.jabzboxing.com/locations/16thandbell/', 'http://stevesdelipgh.com', None, None, None, '1592658343', 'https://techheroes.com', 'https://www.lvscc.com/buffalo', '1592658350', 'http://www.purevanityspa.com', None, None, 'http://www.tjmaxx.com/', None, 'http://www.waterwingsswimschool.com', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.cliffordhouse.com/', None, 'http://www.atenderdentalcareaz.com', None, 'http://vinetavern.com/rural-apache/', 'http://www.lighttouchlaserclinic.com', 'http://www.faouzis.com', 'http://www.eastofchicago.com/', 'http://www.starbucks.com', '1592658389', 'http://curahealth.com', 'http://www.saxbyscoffeeworldwide.com/', 'http://manehaircompany.com', None, None, 'https://www.clothesmentor.com/mayfield-heights/', 'http://www.chin-generation.com', 'http://www.bakedwithlovebakery.com', '1592658410', 'https://www.deserthillsplasticsurgery.com', None, 'http://www.twinsburglibrary.org', None, None, 'http://wendys.com/', None, 'http://www.cannafyl.com', 'http://www.alimento.ca', 'http://www.rockbottom.com/scottsdale', 'http://www.action-door.com/?utm_source=YP&utm_medium=Local&utm_campaign=Network', None, 'http://local.biglots.com/az/phoenix/4085', 'http://www.lagrangeurbaine.com', 'http://www.doitrightplumber.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.princetonclub.net', None, 'http://riddhiskincarespa.ca', 'https://www.bobevans.com/our-restaurants/locations/64?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.hansenpmgt.com/', 'http://www.rembrandtcountertops.com', None, 'http://www.shopneon.com', 'http://www.bouldersgym.com', 'https://www.anitastitch.com', None, 'https://hayscoolingandheating.com', None, None, 'http://www.table89lv.com', 'https://globalwonderland.com/lasvegas/', 'https://www.firehousesubs.com/locations/oh/strongsville', 'https://fullypromoted.com/locations/brooklyn-oh/', 'https://www.dunnedwards.com/directory/store-list/summerlin-078', 'https://www.overheaddoorsales.ca', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZWI', 'http://www.houseofabbeydale.com', 'http://www.goshinkarate.com', 'http://www.chandleraz.gov/default.aspx?pageid=73', 'http://www.earlsgrocery.com', 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', 'https://local.biglots.com/ky/henderson/190?zcp=pd_local_yelp', 'https://costas.market', 'https://locations.pitapitusa.com/ll/US/NC/Cornelius/21726-Catawba-Ave', '1592658521', None, None, 'https://www.walgreens.com/locator/walgreens-2363+s+lindsay+rd-gilbert-az-85295/id=5215', 'http://sc-clinic.com/clinic/richmond-hill/', 'http://www.eaglemtn.com', None, None, None, 'http://fantasynailslasvegas.com', None, None, None, 'http://www.herbboxcatering.com', 'http://countryinns.com', 'http://annwiermanmd.com', 'https://www.casa-brasil.com', 'http://www.all-stargrooming.com', 'http://www.kellyservices.com', 'https://vluxespa.com', 'http://www.GlobulCars.com', 'http://www.planetsmoothie.com/stores/19163', 'https://www.upack.com', 'https://beyondselfstorage.com/location/self-storage-mt-lebanon-pa/', 'http://bridalfashionfraire.com/', None, 'http://foundrylv.com', '1592658582', 'http://www.takesushi.ca', 'http://amyrothandcompany.com', 'http://thedriftwoodgroup.com/restaurants/hodges/', None, None, 'https://www.fatbastardburrito.ca', None, 'http://www.greenbasilrestaurant.com/', 'https://steinberglawgroup.com', '1592658608', 'http://www.fionnmaccools.com', 'https://desertrad.com/locations/southwest-wynn-road', 'http://www.resultslawnservice.com/', None, None, 'https://www.mattressfirm.com/stores/oh/rockyriver/mattress-stores-rocky-river-oh-44116-6955.html', 'http://everybodylovesflowers.com/', 'https://southbeachtanningcompany.com/seneca-commons/', None, 'http://www.iyclv.com', None, None, 'http://www.einsteinbros.com/', 'https://www.enterprise.com/en/car-rental/locations/us/oh/cleveland-heights-3915.html?mcid=iyp:8368400', None, 'http://www.tipsycowmadison.com', 'http://coolblew.com', None, '1592658654', 'http://www.hairnafter.com', 'http://www.20volumesalon.com', 'http://www.liquorstorevegas.com', 'http://realtyexchangeaz.com', None, 'http://www.GoMobileConversions.com', 'https://www.qhrpharmacylv.com', 'https://www.caesars.com/nobu-caesars-palace?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=NobuHotel&utm_content=hotel', 'http://www.fireescape.com/', None, 'http://armadaskateshop.bigcartel.com', 'http://www.kenravago.com', '1592658687', '1592658690', None, None, None, 'http://www.tailblazerspets.com/tailblazers-locations-calgary-inglewood.php', 'http://www.anabelldillonphotography.com', None, None, 'http://www.thelistsalon.com', 'http://www.superstitionah.com', 'https://las-dos-fronteras.business.site', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'http://www.hendrickfiatofconcord.com', None, 'https://www.mattressfirm.com/stores/nc/charlotte/mattress-stores-charlotte-nc-28203-6535.html', 'http://www.wowfactorcakes.com', 'https://www.gscapts.com/apartments/nevada/rancho-mirage/', 'http://www.vape-co.com', None, 'https://www.azpuppets.org', None, 'http://www.wellhunggaragedoors.com', 'http://giannistrattoria.com/', 'http://www.valley-urgent-care.com', 'http://www.ruralking.com', None, None, 'http://www.maplebearusa.com', 'http://www.pghpopcorn.com', 'http://www.aspenortho.com', None, 'https://stafitnowaz.com', 'http://www.expressfactoryoutlet.com/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'https://trainingbybo.com', 'https://www.midwoodguitarstudio.com', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', None, 'https://thehomeschoolroom.net', 'https://www.360propertymgt.com', None, 'http://www.hesterheitel.com/', None, 'http://www.dynamicfitnessandretreats.com', 'https://cutandcolorbylionel.com', None, 'https://ad.doubleclick.net/ddm/clk/458685326;262921492;t', 'http://loftnailstudio.com', None, None, 'https://scribblescoffee.co', None, '1592658819', 'http://noahsarklimos.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.kylesbees.com/', 'https://www.dentguyslasvegas.com', 'http://www.eatrad.com/', 'http://dancingleafspa.com', None, None, 'http://burtonmeats.com/retail/locations/', 'http://www.anitaip.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.easytimecafe.net/', 'https://ad.doubleclick.net/ddm/clk/312231550;139998416;h?https://www.bellagio.com/en/restaurants/harvest.html?dfaid=1&ecid!=yelp_2016', 'http://www.einsteinbros.com/', None, 'http://www.szechwan-garden.com/', 'http://dragonflame.us', 'http://haircutsonwheels.ca', None, None, 'http://angolino.ca', 'http://www.insurelasvegas.net?cmpid=l4u1_blm_0006', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.desertridgeacu.com', None, 'http://gmexperts.com', 'https://www.redroof.com/property/wi/madison/RRI052', 'http://www.davidsonicehouse.com', 'https://www.venezias.com/yelp-deals/', 'https://www.eastsidemazdavw.com', 'http://vertucciofarms.com/', None, None, None, 'http://www.madcatpets.com', 'http://www.olenliving.com/horizonridge', None, 'http://www.cbcc.us', 'https://www.mainevent.com/location/ohio/avon/44011?utm_campaign=localmaps&utm_medium=organic&utm_source=yelp', 'http://jacksonswash.com', 'http://www.pghfilmmakers.org', 'http://forty2supperclub.com', None, 'http://www.petparadiseohio.com/', None, 'http://www.bodyheattanning.com', 'http://aleasylum.com/', None, 'http://herbivore.to/', 'http://sugarbomb216.com', 'https://www.southsidecleveland.com', 'http://www.umghome.com/', 'https://friendlydentalgroup.com/locations/indian-trail/', 'http://lacarnita.com/', 'http://www.miisandwich.com', 'https://www.stonebridgemanor.com', None, '1592658961', 'https://www.mbiaz.com', '1592658965', 'http://www.shell.us/', 'http://www.coppacoffeeandtea.com', 'http://www.eightlimfit.com', 'https://www.burritoboyz.ca/mississauga', 'http://www.drgreenapple.com/', 'https://www.longhornsteakhouse.com/locations/oh/copley/copley-fairlawn/5257?cmpid=br:lh_ag:ie_ch:dry_ca:LHQ121LOCURL_dt:20200619_sn:yelp_gt:copley-oh-5257_pl:locurl_rd:1211', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.1800gotjunk.com/us_en/locations/junk-removal-pittsburgh?utm_campaign=yelp&utm_source=pittsburgh&utm_medium=ubl', None, 'http://www.thedeadhorsecantina.com/', 'http://www.purplereign.net', None, 'http://www.dentistry4kids.ca', 'https://www.petsmart.com/stores/us/oh/cuyahoga-falls-store0519.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://www.weisbrodchiropractic.com', 'https://www.kumon.com/GILBERT-EAST-AZ', 'http://bestpizzapita.com', None, 'http://www.mrosmow.com/', 'http://www.originalpancakehouse.com/', 'http://doubledays.net/', 'http://santosalon.com', 'https://www.choicehotels.com/north-carolina/matthews/quality-inn-hotels/nc675/rates', None, 'http://www.venturepest.com', 'http://www.lashnewyork.net', None, 'https://www.charlesclausendds.com', None, None, 'http://www.brownsshoes.com', 'http://www.relaxologywellness.com', 'https://www.hooters.com/locations/1088-concord-nc', '1592659048', 'http://dollheadslv.com', 'http://www.jamakbeauty.com', 'http://www.felicianotowing.com', 'http://www.healthexpressuc.com', None, None, None, '1592659068', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', None, 'http://www.bronsteinhandcenter.com', 'http://www.peoplesmortgage.com', None, 'http://www.tinderboxcigars.com', None, 'https://www.haircutmenmcknightpittsburghpa.com', 'https://locations.rallys.com/az/phoenix/1345-west-camelback-rd./?utm_source=Yelp', None, 'http://www.kitchenstuffplus.com', None, '1592659096', 'https://www.stronghouseproject.com/pages/gym', 'http://www.prestigebilliardsaz.com', 'https://www.chocolatsfavoris.com', None, None, None, 'http://www.myjewelrycenter.com', 'https://www.kindercare.com/our-centers/chandler/az/000156?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=000156', 'http://oscarstacoshop.com', 'http://www.venetian.com/food-courts.html', 'http://www.carefreetea.com/', 'http://www.marshallretailgroup.com', 'http://www.hermes.com', 'http://www.depotiresandservices.com/auto-services', None, 'http://www.edisonfamilymedicine.com', None, 'https://www.simonmed.com/locations/all/simonmed_imaging__peoria_plaza', 'https://cravingvapor.com', 'http://rossini-s.com/', 'https://www.autozone.com/locations/al/madison/1626-hughes-rd.html', 'https://www.storagewest.com/facilities/boulder-hwy/?utm_medium=organic&utm_campaign=yext&utm_source=yelp', None, '1592659144', 'http://linear295.com', None, 'http://www.mrsbakermom.com', '1592659154', 'http://www.shibuirobatabar.com/', 'http://www.modernhyundaiofconcord.com', 'http://www.lessonswithderek.com', None, None, 'http://dentistryofthecarolinas.com', 'http://www.yourcustomexpress.com', 'http://UNITSstorage.com/locations/arizona/phoenix', '1592659176', 'http://eavestroughers.com', None, 'http://www.pizzanostrainc.com', 'https://www.smartstyle.com/en-us/locations/az/mesa/located-inside-walmart-2768-haircuts-18263.html', 'http://www.officedepot.com', 'http://www.ogleshardwoodflooring.com', 'http://www.dickeys.com/', None, 'http://www.mkautomotive.com/', 'http://honestmaids.co', 'http://symposiumcafe.com/thornhillrestaurants.html', '1592659205', 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', None, 'http://www.marriott.com/hotel-info/phxdr-jw-marriott-phoenix-desert-ridge-resort-and-spa/recreation/ouvsg2x/resort-amenities.mi', None, 'https://www.rmcf.com/OH/Westlake50788', 'http://www.leaksquad.com', None, 'http://radiomariarestaurant.com', None, None, None, None, 'https://1010dilworth.com', 'https://www.starbucks.com/store-locator/store/17761', None, None, None, 'http://www.charlottevitaminsandhealth.com', None, 'http://www.lindadyster.com?cmpid=NGLC_BLM_0006', 'http://www.ovorolo.ca', None, None, 'http://www.ihg.com/holidayinnexpress/hotels/us/en/streetsboro/sbooh/hoteldetail', None, 'http://www.autonationfordscottsdale.com', None, 'https://www.tidedrycleaners.com/locations/las-vegas/las-vegas', 'http://thailahna.com', None, 'http://www.barvolo.com', 'http://www.chatime.com', 'http://yourhealthyfutures.com', 'http://theupsstore.ca/45', 'http://gilscafe.com', None, None, None, 'https://locations.hollywoodfeed.com/nc/huntersville/9129-sam-furr-road.html', None, 'http://c-modcuratedmoderndesign.com', None, None, 'https://batlgrounds.com/axe-throwing-calgary', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, 'http://www.onoirtoronto.com', None, 'http://www.kenzieskuts.com', 'http://www.fmbbq.com', 'http://www.johnfishjewelryschool.com', 'http://www.electrika.ca', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXAK', 'http://christinedang.exprealty.com', 'http://nectarfloraldesigns.com/', 'http://www.ffcommunity.com', 'http://luxuriouslashesbylisa.com', 'http://www.nomadsrestobar.com', 'http://www.circuscircus.com/dining/casino_cafe.aspx', None, 'http://www.badcreditvehicle.com/', 'http://www.hairhouselv.com/', None, 'https://www.givingtreeaz.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'https://www.abdsignsandprinting.com', 'https://www.thejoint.com/arizona/phoenix/arcadia-48011', 'http://www.foodiesonfoot.ca', 'http://www.harvestmeadow.com', 'https://www.refineryresale.com', None, None, 'http://www.firstchoiceautobodyandpaint.com', 'https://www.t-mobile.com/store-locator/in/avon/rt-36-shiloh?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.ecocleanlv.com', None, None, None, 'http://mrflamingo.squarespace.com/#about', 'http://www.urgentcareexpress.com', None, 'http://www.thecakecafeaz.com', None, 'http://www.nccfloors.com', None, None, None, 'https://www.midtownsundriesgrillandbar.com', 'http://www.servicesbysisco.com', 'http://www.tuesdaymorning.com', 'http://backeastbagels.com', 'https://www.josbank.com/store-locator/henderson-nv-475?utm_source=yelp&utm_medium=listing&utm_content=475&utm_campaign=NV', 'http://www.coloredroom.com/', 'http://www.canadacomputers.com', '1592659485', None, 'http://www.sunshineflowers.net/?srccode=yelp_track', 'http://www.hudsonwinefestival.com', 'http://www.canyoncreekvillageapts.com', 'http://www.circuscircus.com/dining/circus_buffet.aspx', 'http://www.juanmeanburrito.com', 'http://www.scootergirltoys.com', 'https://petersendean.com', None, 'http://www.thepigeonman.net', 'http://www.ariacomplex.com', 'http://www.alliancebailbondsaz.com', 'http://hiltongardeninn3.hilton.com/en/hotels/ontario/hilton-garden-inn-toronto-markham-YYZMAGI/index.html?SEO_id=YELP-GI-YYZMAGI', 'https://www.originalmattress.com/store/8/Mayfield-Heights-Ohio-Store', None, None, None, 'http://www.jandjairductcleaning.com', 'http://locations.in-n-out.com/160', 'http://www.torontobuskerfest.com/', None, None, 'http://tacosnritas.com', 'http://altitudeelyria.com', 'http://www.tastybox.net', '1592659572', 'http://www.polishedtoolv.com', 'http://concord.wbu.com', 'http://paramountscreensaz.com', 'http://www.spike-o-matic.com', None, None, 'http://www.pilatesofscottsdale.com/', 'http://www.BloomingRoseEsthetics.com', 'https://locations.churchs.com/az-goodyear-8763', 'http://www.timhortons.com/', 'http://www.cookout.com', 'http://www.mobile-depot.ca', '1592659616', None, 'https://www.halibuthouse.ca/locations/halibuthouse265edward/hours/', 'http://www.awesomecarpetservice.com/index.html', 'http://www.aoclasvegas.com', 'https://www.choicehotels.com/north-carolina/charlotte/sleep-inn-hotels/nc033/rates', 'https://mandarinrestaurant.com/brampton-west/', 'http://www.sushilongueuil.com/', None, 'http://www.acrxpharmacy.com', 'http://www.mellonstreetgarage.com', None, 'http://gaishauserdentistry.com', None, None, 'http://www.socialcoffee.com/', None, None, '1592659675', 'http://www.stopandshop.com', 'http://www.degaetanos.com/', 'https://www.ajimprovements.com', 'http://www.mynewimagesmile.com', 'http://Southern-Nevada.certapro.com/?source=Yelp', '1592659696', 'http://www.grilledexpedition.com/flash.html', None, 'http://www.stavebankflorist.com', 'http://www.eliteuniformsonline.com', None, 'http://www.aurabontems.com', None, 'http://www.mainapplianceservice.com', None, 'http://www.gabesstores.com', 'http://www.katsvillagecoinlaundry.com', 'http://www.dovecleaners.com', 'http://www.shimerzach.com', None, 'http://www.hm.com', None, None, 'https://www.rampartdentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, None, 'http://www.alkaspringswater.com/', None, 'http://www.temakiexpress.ca', None, 'http://www.timhortons.com/', None, 'http://symposiumcafe.com/northyorkrestaurants.html', 'http://www.cameracompany.com', None, None, 'http://stylebyjen.com', '1592659794', None, None, None, 'https://advancedpaincare-nv.com', 'http://www.fitness19.com', None, 'http://eggsandkabob.com', 'http://www.clekeys.com', None, 'http://www.advancebackandneck.com', 'http://www.avantderm.com', 'http://hauntedlv.webs.com', 'http://www.jadenscatering.com', 'http://www.exotixstudios.com', None, 'http://homesforsale-lasvegas.com', 'https://www.thevoid.com/locations/virtual-reality-las-vegas/', 'http://www.frankiebunz.com', None, 'http://thealtkey.com/', 'http://www.marshallsonline.com', 'http://rebeccalynnstudio.com', 'http://www.mrhero.com', 'https://www.olympusproperty.com/cactus-forty-2-phoenix-az/', '1592659885', 'http://www.aireserv.com/east-valley/', 'https://www.kellyjorncook.com', 'https://stores.nordstromrack.com/us/nc/charlotte/9563-s-blvd?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=641&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', None, None, 'https://www.cricketwireless.com', 'http://www.arizonafarmersmarkets.com/', None, 'https://www.kcaikendds.com', 'http://degreeac.com', 'http://phoenixicemanac.com/residential-air-duct-cleaning/', 'http://jetroomrestaurant.com/', 'http://eudociasalonandspa.com', 'http://ufcgym.com/northlasvegas/?utm_campaign=WebHomepageRefID34504&utm_medium=Display&utm_source=Yelp', 'http://www.shaanxibiangbiang.com', 'http://www.myphoenixelectrician.com', None, 'http://revivalchili.com', None, 'http://www.nissanairport.com', 'https://wheelhousesjo.com', None, None, None, None, None, None, 'https://www.cantaritosmexicangrill.com', 'http://jw-patisserie.com', 'https://maidofhonourcleaning.ca', 'http://www.millerlashhouse.ca/index.html', 'https://www.frysfood.com/storeHours?store=66000129', 'http://www.tallmadgechiro.com', 'http://www.alluringpermanentmakeup.com', 'http://www.barrelandfork.com', 'http://www.honoraz.com', None, 'http://peaceinjesus.org', None, 'http://www.phoenixaffordablemoving.com', 'http://www.sonnyschandler.com', None, 'http://fifthavenueplacepa.com', None, 'https://repairboyz.ca', 'http://www.ductwhip.com/', 'http://www.pizzapino.ca/', 'http://www.cuttingedgesewing.com/', 'http://www.starbucks.com', 'http://www.herbalnailsmesagilbert.com', 'http://www.allurehairspa.net', 'http://randalljcraig.com/', 'http://www.sunshinedrycleaner.com', 'http://www.continental.com/web/en-US/content/travel/airport/lounge/locations/all.aspx', 'http://www.mattressfirm.com', 'http://hmartca.com/hmart/?page_id=19', 'http://www.hqsalonspa.com', 'https://tehransupermarket.business.site', None, None, 'http://www.ferris360.com', None, None, 'http://www.dominos.com', None, 'http://www.sienaanimalhospital.com/', 'http://www.carlsairconditioning.com', 'http://www.rcc-ea.com', 'http://premierbodyworkmadison.com', 'http://redrock.clarkcountynv.gov/parksloc/details.aspx?park=11', None, 'http://www3.hilton.com/en/hotels/arizona/hilton-phoenix-mesa-MESHPHF/dining/index.html', 'http://www.lviglobal.com', 'http://livnlo.com', None, 'https://locator.chase.com/az/gilbert/5238-s-power-rd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://oasiswindowtint.com/', '1592660153', 'http://www.ajsfinefoods.com', None, 'https://www.saksfifthavenue.com/locations/s/beachwood', None, 'http://Www.Atlanticconcretecoatings.com', 'http://pjhamburgers.foodpages.ca/', None, None, None, 'https://www.ugg.com/stores/s/las-vegas-north-premium-outlets', 'http://www.blackchile.com', 'https://www.excalibur.com/en/amenities/the-spa-at-excalibur.html', 'http://greensandproteins.com', 'http://jamilamiraclebrows.com/Jamila/Welcome.html', 'http://jdihotdogs.com', None, '1592660207', 'http://www.thestranditalian.com/', None, 'http://www.skinandlaserlv.com', 'https://neoskincenter.com', 'http://communitysupermarket.com/', 'http://www.bajaautos.com', 'http://www.artetcpictureframing.com', None, 'http://www.goodwillaz.org/', None, 'https://www.wyndhamhotels.com/hotel/52782?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52782', None, 'http://www.costco.com/warehouse-locations/thomas-road-phoenix-az-465.html', 'http://www.judyspizza.ca/', 'https://www.valvistaanimalhospital.com', None, None, None, 'http://www.perplexity.ca', 'http://hybridsalon.com/contact-us/', 'https://www.supercuts.com/locations/az/mesa/gilbert-gateway-town-center-haircuts-90179.html', 'http://stotnstotcpa.com/', 'http://www.onenevada.org', 'https://timanwindowtreatments.com', 'http://www.finishline.com', 'http://www.rotorooter.com', 'https://www.weightwatchers.com/us/find-a-meeting/37302/weight-watchers-grand-village-surprise-az', 'http://capellibabe.com', None, 'http://cjautorepair.wix.com/lasvegas', None, 'https://www.petsmart.com/stores/us/nv/las-vegas-store1153.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.shutterdoctoraz.com', 'https://www.nofrills.ca/store-locator/?storeId=3659', None, 'http://ricksgoodeats.ca', None, 'http://www.Foundationchiroaz.com', 'https://www.williams-sonoma.com', 'http://clickserve.dartsearch.net/link/click?lid=43700026045810632&ds_s_kwgid=58700003267206446&ds_url_v=2', 'http://www.gastonymca.org/locations/warlick-family-ymca/', 'http://www.itamealaval.com/', 'http://www.newhorizonswomenscare.com/home/chandler-office.php', None, 'http://www.t-mobilearena.com', 'http://www.tutierra.ca/index.html', 'https://www.sprint.com/storefronts/bd/sprint-cleveland-oh-44109-fcs-1798/?ecid=SEO:Yelp:2020_Q1:LastMile', None, 'https://www.getgocafe.com/stores/pa/pittsburgh/baum-blvd-getgo/3064', 'http://www.paarplumbing.com', None, None, 'http://www.dermaartmedspa.com', 'http://www.torontocolonics.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700006431963542&ds_s_kwgid=58700000443428492&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, None, 'http://thecarpetmonkeys.com', None, None, 'http://gracechurchmentor.org/', 'http://gastonia.paulmitchell.edu', None, 'http://www.redbarandloungewestpark.com', 'http://www.righttech.ca/', 'https://www.lakewoodexterminating.com', 'http://www.thediamondcompany.ca', None, None, 'http://earthtonesaz.com', None, 'http://finelinesma.com', 'http://www.quiznos.com', 'http://www.bartelltheatre.org', 'http://redmountainroofing.com', 'https://www.circlek.com/store-locator/us/cuyahoga-falls/1790-4th-street/m5411', 'https://bargainstorage.com/arizona/self-storage-phoenix-az/85023-self-storage/606', 'https://www.mazdaofgastonia.com', 'http://www.beyondstonesolutions.com', 'http://www.thevinylpi.com/', None, None, 'http://www.petplanethealth.com/stores/country-hills-town-centre/', 'http://www.gioiabeautybarspa.com', None, 'https://Valentineteam.com', 'http://www.tapphong.com', None, 'https://www.scottsdalesunless.com', 'http://www.cfgilbert.com/', 'https://www.eyeglassworld.com/store-list/goodyear-az-85338/', 'http://www.redribbonbakeshop.us', 'http://adfarm.mediaplex.com/ad/ck/24347-208274-18214-4', 'http://www.redmangousa.com', 'http://www.tasteofjaffna.ca', 'http://www.libertydevelopment.ca', None, 'http://waypointhomes.com', 'http://www.24yessisprek.com', 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', 'http://www.sincitynails.com/', 'http://stores.disneystore.com/oh/north-olmsted/391', 'http://locations.michaels.com/PA/TARENTUM/7757/', 'http://www.arizonagasproducts.com', 'https://www.tedwiens.com', None, 'http://www.spa-uptown.com', None, 'http://salvagedbeautynoda.com', None, 'http://www.mistypinespetcompany.com', 'http://blackbriik.com', 'http://www.speedeeoil.com/Locations/Oil-Change-Tune-Up-Concord-NC-28027', 'http://www.thea1way.com', 'http://www.marbleslab.ca', 'http://mountainbean.com', 'http://willoscape.com/', 'http://www.krahfamilydentistry.com/', None, None, 'http://eddiebashacollection.com', 'http://www.animalkingdomaz.com/', 'https://lvfarmersmarkets.wixsite.com/lvfm/bruce-trent-park', 'http://www.wainwrightdentistryaz.com', 'https://recreation.scottsdaleaz.gov/Start/Start.asp', 'http://www.gardenlaurels.com', None, 'https://www.thestudiophoenix.com', 'http://www.cortebella.net/Dining~288182~14243.htm', 'www.bourbonstreetaz.com', None, None, None, None, 'http://www.sothan.com?cmpid=PKKC_BLM_0006', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://www.purityskinandbody.com', '1592660660', 'http://www.absoluterv.com', 'http://salumibar.ca', 'http://www.pcmforless.com', None, 'http://www.goldenwokaz.com', 'https://smartwrap.com', 'http://www.coldstonecreamery.com/stores/21073', 'http://www.gianteagle.com', 'http://www.reliablecarpet.ca', 'http://www.goodlifevapes.ca', 'http://daisymountainpainting.com', 'http://www.labcorp.com', None, '1592660706', 'http://www.rossstores.com', 'http://robertostacoshop.com', None, 'http://www.7-eleven.com/?yelp=35551', 'http://www.insightpropertynv.com', None, None, None, None, 'http://www.somasleep.ca', 'http://www.trilogygolfclub.com/vistancia', 'http://locations.rentacenter.com/arizona/phoenix/85016/2341-e-indian-school-rd/', 'http://pghfirm.com', 'https://www.answerarizonatelemessaging.com', 'http://www.flushotsusa.com', 'http://www.paworldofrugs.com', None, 'http://www.thaihouse-az.com', 'https://www.virtualbrokers.com/', 'http://lasvegas.jiffylube.com/Locations/Store/2668/2583-WINDMILL-PKWY-HENDERSON-NV-89074-5358', 'http://greystoneshealth.com', 'http://www.willicklawgroup.com', 'http://www.gigiscupcakesusa.com/scottsdalearizona', 'http://www.academyofbeautyprofessionals.com/madison/', 'http://www.activegreenross.com/tire-centre/etobicoke/21-186-the-queensway-etobicoke?postcode=m8y1j3', 'http://www.salonverveinc.com/', None, None, 'http://www.arizonaironfurniture.com', 'http://www.snakesandlattes.com/location/annex', 'http://www.barristersgastonia.com', None, 'http://www.homesense.ca', 'http://samsxpresscarwash.com/denver', 'http://www.districtcleveland.com', None, 'http://www.earthboundtrading.com', 'http://www.northvalleydiesel.com/', 'http://www.wendys.com/', 'http://pandashowvegas.com/', None, '1592660841', 'http://charmeck.org/mecklenburg/county/ParkandRec/Parks/ParksByRegion/NorthRegion/Pages/RamseyCreek.aspx', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.wordenmartingm.com', None, 'http://www.ircahotelservices.com', 'https://www.karmacampervans.com', 'http://3rddistrictsalon.com', 'http://www.ranchograndemarket.com', 'http://nodavethosp.com', 'http://www.battleartsacademy.ca', 'http://arbys.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, 'https://www.911restorationlasvegas.com', 'https://www.onenevada.org/?utm_source=Yelp&utm_medium=Site&utm_campaign=MainPage', 'http://www.simonlawaz.com', 'http://www.strategicresumegroup.com', 'http://www.optikboutik.com', None, 'http://thebuyandsellstore.ca/', 'http://www.goodwillaz.org', 'http://www.ilovetacosmiddleton.com', 'http://icebergatboulevard.com', 'http://www.acmelv.com', 'http://www.launicahuntersville.com/', 'http://www.tinapronails.com', None, 'http://www.springrolls.ca', 'http://www.hansons-lawns.com/', 'https://www.mattressfirm.com/stores/az/glendale/mattress-stores-glendale-az-85308-7021.html', None, 'http://www.victoriassecret.com', 'http://www.cleupscaleresale.com', 'http://www.hirollersbarbershop.com', 'http://www.starbucks.com/store/9334/', '1592660960', None, 'http://www.realestatekasey.com', 'https://union.wisc.edu/dine/find-food-and-drink/ginger-root', 'http://www.cartechaz.com/index.html', 'http://www.dunkindonuts.com', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'https://www.chipotle.com?utm_campaign=cmg_yelp_listings&utm_medium=Yelp-listing&utm_source=Yelp', 'http://neginpastry.com', 'http://www.sabaandfowler.com', None, 'http://www.hardwood-lumber.com', 'http://www.centerforaltmed.com/', 'http://www.fatburgercanada.com', None, 'http://www.preston.industries', None, 'http://escobarsrestaurant.com/', 'https://www.chick-fil-a.com/arboretum', None, 'http://www.bombaybhelrestaurant.com', None, 'http://adcendance.com', 'https://www.smartstyle.com/en-us/locations/az/scottsdale/located-inside-walmart-2766-haircuts-460.html', 'https://accentscreens.com', 'http://tinfrontcafe.weebly.com', 'https://conciergemedicinesummerlin.com', '1592661058', None, 'http://www.ArchRentals.com', 'https://stores.petco.com/az/gilbert/pet-supplies-gilbert-az-1104.html', 'http://locations.harristeeter.com/nc/matthews/273/', 'http://www.cicis.com/locations/az-phoenix-2270-n-75th-ave', '1592662709', None, None, None, 'http://www.torontocolonics.com/', 'https://playatgila.com/dining_restaurant/?id=5958', 'http://www.coach.com', None, None, None, 'http://www.oakvilletech.ca/', None, None, 'http://www.endurosport.com', 'https://bostonpizza.com/en/locations/sunridge.html', None, 'http://www.tutortime.com/your-local-school/charlotte-nc-6120/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', '1592662763', '1592662767', 'http://www.skinatomylaserclinic.com/', 'http://www.restaurantrube.com/accueil', 'https://www.rubios.com', 'http://www.snaptowing.com', None, 'http://schnitzelhub.com/', 'http://www.realfruitbubbletea.com', 'http://local.firestonecompleteautocare.com/arizona/mesa/1840-n-lindsay-rd/?lw_cmp=IYP_YPC_MLP_349492', None, 'http://www.robertscatering.net/', 'http://www.dreamingdragonsmassage.com', 'http://www.bar97.ca', None, 'http://www.my3girlsbakery.com', 'https://turtlejacks.com/locations/clarkson/', 'http://www.uniquitiesfurniture.com', None, None, 'http://doughto.com', 'http://www.quickstop1.com', 'http://www.vintnerwinemarketnc.com/', None, 'http://www.arizonadynochip.com', 'http://www.7plusinc.com', 'https://palmbeachtan.com/locations/OH/Streetsboro-State-Route-303/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=CLE', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'http://www.clevelandorchestra.com', '1592662863', None, None, None, 'http://www.gardenofeatingpizzeria.com', 'http://thevillageeyecare.com', None, 'http://www.trutherapeutics.ca/', 'http://www.earnestrestaurant.com/', 'http://www.fixmyrust.com', 'http://crysstyleshairboutique.com', 'http://powerwashphx.com', 'https://www.bankofamerica.com/', 'http://www.victra.com', 'http://carmelautomotiveaz.com/', 'http://www.clevelandirish.org', 'http://www.foodbasics.ca', 'http://alsbeadsandsilver.wix.com/alsbeadsandsilver', 'http://www.destinationxl.com/mens-big-and-tall-store/storelocator/storeDetails.jsp?storeNumber=+9731', 'http://communitymontessoriphoenix.com', 'http://vinaautomobile.com', 'http://www.meltgrilledcheese.com', 'http://plumbingmastersaz.com/', None, None, 'https://upfreshkitchen.com', None, None, None, None, None, 'http://www.babessportsbar.com/', 'https://www.swatbugkillerspestcontrol.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592662975', 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', 'https://www.aaautocarelv.com/locations/decatur-blvd/', None, 'http://www.wangsexpressphoenix.com', 'http://www.growlerstogogo.com', 'http://www.milkandhoneyjcc.com', None, 'http://amerifitfitnessclub.com', 'https://www.botanistofthevalley.com', 'http://www.theepicureshop.com/', None, 'http://kennethcole.com/?om=ADV-media:YelpListings-2014:spring-2014:yelp:::KCP_com', None, None, '1592663023', None, 'https://local.fedex.com/oh/twinsburg/office-1672/', 'http://pawswhiskersandwags.com', 'http://www.starshipearth.us/se02.html', '1592663039', 'http://naturellenailsspalv.com', '1592663046', 'http://www.humblepieusa.com/', 'http://www.cavecreekfitness.com', 'http://www.bankofamerica.com', 'http://www.mesaaz.gov/parksrec/aquatics/pools/Carson.aspx', 'http://ahipoki.com', 'http://www.ubreakifix.com/locations/phoenix', '1592663063', 'http://sparklecleanaz.com', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_633', 'http://brian-craveiro.myhomehq.biz', None, 'http://www.heidiboutique.com', 'http://www.homedepot.com/l/Curity/ON/Toronto/M4B-3L8/7012', None, 'http://www.hihealth.com/storelocator/view?id=40', 'http://www.hertz.com', 'https://cityseamless.com/service-areas/las-vegas', 'http://www.aroojis.com', None, None, 'http://www.michaeljenningsphotography.com', '1592663100', None, '1592663105', 'http://www.desertskyanimalhospital.com/', 'http://www.desertplasticsurgery.com', 'http://paramusictoronto.com/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'https://www.skinfactorytattoo.com/henderson-tattoo-shop/', 'http://newagecosmeticsurgery.com', 'http://www.usadawgs.com', '1592663128', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.alexisbrothersbalance.com', 'http://www.marriott.com/hotels/travel/pitmr-courtyard-pittsburgh-monroeville', 'https://www.campk9madison.com/?utm_source=yelp&utm_medium=social', 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', 'https://www.thebeachhouseaz.com', 'http://www.chopstickshouse.ca', 'http://www.7-eleven.com/?yelp=29384', None, None, 'http://sanfranciscoplace.ca/', None, None, 'http://www.ishsalon.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.salonone.ca', 'https://www.stagshop.com/?utm_campaign=StagShopYelp&utm_medium=cpc&utm_source=Yelp', None, 'http://www.trophyfactorylv.com', 'http://www.pippo.ca/', 'http://www.thirstycowboys.com/', 'https://www.carzilla.ca', 'http://theloftlasvegas.com', 'http://www.bodyspasalons.com', 'https://www.envymygarage.com', None, '1592663198', None, None, None, 'http://www.movement.com/chad', None, None, None, 'http://www.cafefresco.ca/', 'http://santanvillage.doghaus.com', None, 'https://stores.loft.com/outlet/us/nc/charlotte/5512-new-fashion-way.html', None, 'https://www.luxdentalscottsdale.com', 'https://www.anytimefitness.com/gyms/288/Las-Vegas-NV-89139/?utm_source=yelp&utm_medium=local', 'http://www.teavana.com/', None, 'http://www.allinfitnessandwellness.com', 'http://www.jordantax.com', 'http://www.arizonaflooringremodeling.com/', 'https://www.bestwestern.com/en_US/book/hotel-rooms.61099.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:61099', 'http://www.fetchdoggiestore.com', 'http://www.rkmontecitoapts.com', None, None, None, None, '1592663262', 'https://www.chilis.com/locations/us/ohio/n-olmsted/n-olmsted/', 'http://www.planetfitness.com/gyms/charlotte-whitehall-nc-125?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.shoparboretum.com', None, 'http://www.transartnc.com', 'http://www.odjibik.com', 'http://www.chandleraz.gov/aquatics', 'http://www.vssg.net/', 'http://www.dailypressjuicery.ca', 'http://Www.winwinwindowcleaning.com', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', 'http://www.frommtokyo.com', None, 'http://www.floweramacleveland.com/middleburg-hts-location/', 'http://www.portofsubs.com', 'http://www.independentelectricaz.com', 'http://www.gioiabeautybarspa.com', 'http://www.ScoundrelsPubII.com', 'http://www.irent4you.com', 'http://www.tvmounting.net', 'http://www.gomoxiestudio.com', 'https://katherines-family-restaurant.business.site', 'http://www.summerspointapts.com', None, None, 'http://www.jambajuice.com', 'http://www.brownchiro.com', None, 'https://mrsub.ca', 'http://ristoranterosina.ca', 'http://www.boosterjuice.com', 'http://www.kfc.ca/store/sunrige-mall-101-2525-36-st-ne-calgary', 'http://www.fullforce.fitness', 'http://www.sunsetgardens.com/', None, 'http://www.studiovino.com', 'http://Autorelocationspc.com', 'http://www.merchantfirearms.com', 'https://www.aspendental.com/dentist/oh/brooklyn/7351-northcliff-ave?utm_source=yelp&utm_medium=lociqyext&utm_campaign=Brooklyn%2COH%7C%7CBroklyn_OH%7C%7C6404&utm_content=listing', '1592663361', 'http://www.shoizakaya.com', 'https://www.villaseast.vegas', 'http://www.sanfrancescos.com', 'https://theirishhare.com', 'http://www.brewnorth.com', 'http://www.entegrityent.com', 'http://www.mcnabbplumbing.com', None, 'http://gtdh.ca', '1592663387', 'https://bolster-dehart.com', 'http://www.foxandjanesalon.com/toronto', None, 'http://www.chrislesalon.com', 'http://www.slofoodsaz.com', 'http://www.sweetapplebeauty.com', 'http://www.korteksolutions.com', 'http://owlcleaners.com', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=101357', 'https://www.aaautocarelv.com/locations/aa-auto-care-sunset-rd/', None, 'http://thelockhart.ca', 'http://www.platosclosetcalgarynortheast.com', 'http://www.costco.com', 'http://www.aztecanimalhospital.net/', 'http://bloomsalonaz.com', 'http://www.blackforestwood.com', 'http://Www.mycharlottevet.com', None, 'https://www.sprint.com/storefronts/bd/sprint-phoenix-az-85022-fcs-1908/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.lavenderroseflowers.ca', 'http://www.JimmyJohns.com', 'http://www.jiffylube.com', 'https://rsigrowers.com/index.html', 'http://www.tuffshed.com/phoenix-mesa-peoria/', 'https://www.storage-mart.com/calgary/5th-street-southwest?utm_campaign=yelp_paid&utm_source=yelp&utm_medium=paid&utm_content=3302', '1592663454', 'http://www.azboardsource.com/', None, 'https://www.kiwilocoyogurt.com/5043/Chandler-home/', None, 'https://www.azbrothersmoving.com/?utm_source=Yelp&utm_medium=CPC', 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-west-tempe?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-west-tempe', 'https://palmbeachtan.com/locations/NC/Charlotte-East-Woodlawn-Road?utm_source=Yelp&utm_medium=banner&utm_content=website&content=AUG', 'https://www.homedepot.com/l/Pecos/NV/Las-Vegas/89120/3316?cm_mmc=seo-yelp&', 'http://www.calderonmed.com', 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://www.brusters.com/cornelius', None, 'http://clubfortunecasino.com/dining/', 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store121', 'http://www.bk.com', 'https://www.sonoraquest.com/find-a-location/glendale-59th-ave-eugie/', None, 'http://www.helzberg.com', None, 'http://www.goodwill.vegas/thrift-store-68-4580-west-sahara-avenue-las-vegas-nv-89102/', 'http://www.ballantynejewelers.com', None, None, 'http://www.ultimateproperties.com', 'http://checkpointdoorandlock.ca', 'http://www.fashionbyrobertblack.com', '1592663522', '1592663525', 'http://www.excelhonda.com', 'http://www.vibelashandwaxstudio.com', 'http://www.momoskebab.com/', 'http://www.evilswinebbq.com', 'https://locations.timhortons.com/ca/qc/laval/3099-de-la-concorde-est.html', 'https://www.texasroadhouse.com/locations/arizona/peoria', 'http://www.kaykayrealty.com/lofts10-apartments/property-29/', None, 'http://www.dunkindonuts.com', None, 'http://www.greatclips.com', None, 'https://www.anytimefitness.com/gyms/141/Madison-AL-35758/?utm_source=yelp&utm_medium=local', 'http://glenncustom.com/', None, 'http://www.niagarastreetcafe.com', 'http://www.oldnavy.com', 'http://www.bulkbarn.ca/', 'http://www.thehoneyglazedham.com', 'http://www.redrockcountryclub.com', 'https://www.metropcs.com', None, 'https://elementsmassage.com/south-mesa', 'http://www.torontopubliclibrary.ca/hou_az_rn.jsp', 'http://www.thesafekeeper.com', 'http://www.airparkpaknship.com', 'http://snipits.com/locations/huntersville', None, 'http://www.arrowheadlakeschiro.com', None, 'http://www.pizzanova.com/locations/markham.html', 'http://www.gandolfosdeli.com', None, 'http://www.ajsfinefoods.com', 'http://www.tiffany.com', 'http://www.kannapoliscomputer.com', None, 'https://locations.theupsstore.com/az/glendale/20118-n-67th-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.pizzashab.ca', None, 'http://www.homegoods.com', 'http://www.sarkujapan.com/', 'http://www.bootstaronline.com', None, 'https://www.kumon.com/SCOTTSDALE-SHEA-SCOTTSDALE', 'http://www.valleywidecustompainting.com/', None, 'http://www.manifestcle.com', 'http://www.katsurdental.com/dentist/pittsburgh/west-mifflin/', None, 'http://locations.michaels.com/va/woodbridge/4816/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://littlemountainbrewing.com', 'http://crossfitdavidson.com', 'http://regissalons.com/salondetail/default.asp?salonid=3861', None, None, '1592663661', 'http://www.24hourfitness.com', None, None, None, 'https://www.pizzahut.ca/store-details/store-R31401/pizza-hut-Toronto', 'http://www.usps.com', 'http://www.archkingwestdental.ca', 'http://www.yellowfinlogistics.com', 'https://www.valefamilydental.com', 'https://www.costcobusinesscentre.ca/warehouse-locations/scarborough-business-centre-scarborough-on-595.html', 'http://www.fortyorkpizzeria.com', 'https://sweetfrog.com/locations/store/sweet-frog-monroe-nc', 'http://www.nothingbutnoodles.com/', None, None, 'http://www.backstopsportspub.com', 'https://www.umeaz.com', 'http://www.amicotoronto.com', 'http://www.vtheshow.com', 'https://local.safeway.com/safeway/az/goodyear/440-n-estrella-pkwy.html', 'http://www.phoenixdancecooperative.com', 'http://www.marshallsonline.com/store-finder/204', 'http://www.bibabexpress.com', 'https://www.paradisewindowcleaning.org', 'http://spicewellnesscalgary.ca', 'http://www.pulaskiclubaz.org', 'http://Filmworkzlv.com', 'http://www.svdpmadison.org/shop/stoughton/', None, 'http://www.nicholasyale.com', 'https://www.carolinablindcrafters.com', None, '1592663741', None, 'http://www.hcpnv.com/clinic/wynn', 'http://whitewhalebookstore.com', 'http://www.bravionline.com', 'http://www.ultragloss.biz/', 'https://www.bannerhealth.com/locations/tempe/banner-health-clinic', 'http://www.OTGexp.com', 'http://www.boarsandwiches.ca/', 'https://ad.doubleclick.net/ddm/clk/434279230;236814625;g', 'http://www.lcbo.com', 'http://spyha.pucksystems.com', 'http://wyn.lv/StrattaRestaurant', 'http://kahunaville.com/kahunaville-o2-bar/', 'https://www.chevronwithtechron.com', None, 'http://www.paninisgrill.com/locations/willoughby/', 'http://www.barksnpurrs.com/', None, 'http://www.siciliansidewalkcafe.com', 'http://www.pixyst.com', 'http://www.canadaselectwindows.ca', None, 'http://www.4rentweekly.com', 'http://www.burgerking.co.uk/', '1592663824', 'http://www.azdem.org', 'http://www.wendys.com', 'http://www.bluenosefc.com', 'http://bivonainsurance.com/', 'http://www.thecaptainsboil.com?utm_source=Yelp&utm_medium=Click&utm_campaign=ON_16640Yonge&utm_content=mainlink', 'http://www.campbowwow.com/pittsburgh-highland-park', 'http://www.gdconstruction.net/', 'http://www.costplustwenty.com', 'http://www.oakleycarpetcare.com', None, 'http://www.redandwhiteappliance.com', 'http://www.quiktrip.com', 'http://www.actiondoorandwindow.com', 'http://www.starbucks.ca', 'http://sneaky-dees.com/', None, 'http://neurocenterlv.com', 'http://secondstoryaz.com', 'http://www.petco.com', 'http://www.gandmautoglass.com', None, None, None, 'http://nbmoving.com', 'http://www.vehiclewraps.vegas', None, 'http://www.cupkajoe.com', 'http://www.holidayinn.com/hotels/us/en/fountain-hills/fthaz/hoteldetail', 'http://www.velvetstyle.ca/', 'http://mirage.com/restaurants/carnegie-delicatessen.aspx', None, 'http://radiusccc5.com/xtremeautobodyaz/', None, 'http://masalamixindia.com', 'http://shimalimousine.com', None, 'http://www.heisleytire.net/', 'http://www.silverandsagejewelry.com', 'http://villagevinyl.ca/', 'http://www.silkelephant.net', 'http://www.willowdaleanimalhospital.com/', None, None, 'http://www.haldiaz.com', None, 'http://www.ftbbq.com', 'http://www.cmu.edu/dining/locations/tartan-express.html', 'https://www.loftone35charlotte.com', None, 'http://www.aaa.com', 'http://www.robinsonautomotive.com/', None, 'http://locations.einsteinbros.com/az/scottsdale/6501-e-greenway-pkwy-bldg-5.html?utm_source=storelocator', None, None, 'https://www.stampedeplumbing.com', 'http://www.motherearthmaids-oc.com', 'http://santorasnv.com', 'http://www.braddahsislandstyle.com', 'http://www.rollingindoughbakerylv.com', 'http://www.redrockmadison.com', None, 'http://www.toronto.ca/animal_services/index.htm', 'http://www.weissguysaz.com', 'http://grocery.gianteagle.com/pd/stores/OH/Lyndhurst/Giant-Eagle-Legacy-Village/925B1168', 'http://www.lvtint.com', None, None, None, 'https://www.mikesautoglasscharlotte.com', 'http://www.waterbeancoffee.com', 'http://acexpertrepair.com', 'http://www.el-zaribah.org', None, 'http://www.littlecaesars.com', 'http://www.zales.com', 'http://www.discounttire.com/dtcs/makeAppointmentForStore.do?sc=AZP-40&utm_source=Yelp&utm_medium=iyp&utm_campaign=YelpIYPSA', 'http://www.chezcora.com/', None, 'http://popeyes.com', 'http://www.pourcleveland.com', None, None, None, '1592664119', 'http://www.fywoodwerks.com', None, None, 'http://www.timhortons.com/', 'http://www.aramark.com/', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=14314', None, 'http://appliancerepairadvisor.com', 'http://www.cofdance.com', 'http://www.dominos.com', None, 'http://www.ginobros.com', 'https://www.visioncenterslv.com/summerlin/', 'http://www.raybernmotors.com', 'http://www.souvlakiexpress.com/', 'https://regenerate-works.business.site', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'http://www.carters.com/home?id=carters&cm_mmc=Retail-_-Carters-_-Yelp-_-April', 'https://bostonpizza.com/en/locations/st-jean-sur-le-richelieu.html', None, 'http://www.rexall.ca/storelocator/store/604', 'http://www.luxelasheslv.com', 'http://columbiaroad.org', 'http://certifiedabc.com', '1592664201', 'http://www.ofacedoughnuts.com/', 'http://calibercollision.com', 'https://www.mexicanelmesonrestaurant.net', 'http://www.malena120.ca', None, 'http://www.activehealthlasvegas.com/', 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', 'https://locator.chase.com/az/tempe/4714-s-rural-rd?jp_cmp=rb/LocalListings/aff/branch/na', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.distincthairdesign.com', 'http://www.gnc.com', 'http://atasteelecreek.com/', 'http://www.greenthumbcleaningandorganizing.com', 'https://www.solidkustomz.com', 'https://www.walgreens.com/locator/walgreens-15514+w+waddell+rd-surprise-az-85379/id=7933', 'http://www.dunkrestaurants.com', 'https://www.cellularsales.com/stores/verizon-1995-w-ellit-rd-chandler-az-85224/', None, None, None, None, None, None, None, 'https://locations.monro.com/pa/monroeville/3754-william-penn-hwy?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://www.frysfood.com/', 'http://www.chezcora.com', 'http://www.mexikhan.ca', 'http://www.napoleonspizza.net', '1592664302', 'http://www.streetsofnewyork.com', None, None, 'https://www.wm.com/us/residential/curbside-waste-pickup?cmp=yelp_cpc_omr_res_Chardon_X_cpc_organic_X&utm_source=yelp&utm_medium=search&utm_campaign=omr&utm_content=res_Chardon_X_cpc_organic_X', None, 'http://www.topgunburgerto.com', None, None, 'http://cityscapephoenix.com/', 'http://www.toys2try.com/', 'https://www.vohwinkellaw.com', None, 'https://www.choicehotels.com/arizona/chandler/comfort-inn-hotels/az373/rates', 'http://www.audiosolutionsinc.com', '1592664349', 'https://www.regissalons.com/locations/oh/fairlawn/regis-salon-summit-mall-haircuts-3503.html', 'http://www.ucbaby.ca', None, None, None, None, 'http://www.exoticsracing.com', 'http://mosgoldenpretzel.com', 'http://www.highlinebrewing.com', 'http://esalerugs.com/', 'https://customclipspetgrooming.com', None, 'https://locator.chase.com/nv/las-vegas/6460-sky-pointe-dr?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.bankofamerica.com', 'https://americanplumbingaz.business.site', 'http://www.scooptacular.com', None, 'http://countertopshoplv.com', None, 'http://jackastors.com/location-map/37/', 'http://www.highlanderwine.com', 'http://www.getsims.com', None, 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'https://solefootandankle.com', 'https://www.akidasushi.com', None, 'http://www.batruplasvegas.com/', 'http://www.bubbles.ca', 'https://locations.nekterjuicebar.com/ll/US/AZ/Scottsdale/6137-North-Scottsdale-Rd*-Ste_-105?utm_source=yelp&utm_medium=link&utm_campaign=Hilton-Village&utm_content=URL', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'https://www.rogersinsurance.ca/calgary-rogers-insurance-office', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.cardenasmarkets.com/', 'http://www.autovalueparts.ca/locations/ab/5/horizon-32nd-avenue-ne-avh-calgary', 'https://npavliklaw.com', 'https://www.choicehotels.com/michigan/monroe/quality-inn-hotels/mi389/rates?pmf=yelp&mc=blypypaf', 'http://www.henryfence.com', 'http://www.bedbathandbeyond.com', 'http://www.loscabosapts.com', 'http://www.serviceking.com/locations/service-king-green-valley?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://www.jollybobs.com/', 'http://custodiosmeatsandeats.com', 'http://www.7-eleven.com/?yelp=29384', 'http://www.petro-canada.ca/en/locations/find-a-gas-station.aspx?MODE=DTS&ID=259', None, 'http://oasistozen.com/', None, 'http://pittsburgh-painting.com', 'http://www.worldmarket.com', 'https://www.redlobster.com/locations/list/pa/pittsburgh/6150-robinson-center-drive', 'http://www.thelovestore.com', 'http://www.genesanes.com', 'http://www.usedcarworldwestpa.com', 'http://www.kaqunlv.com', 'http://smittys.ca/', 'http://citybrewtours.com/pittsburgh', 'http://www.nvfm.com/', 'http://www.catawbariverantiquemall.com/', 'http://www.californianails.com/', None, 'https://www.popeyes.com/store-locator/store/restaurant_84969', 'https://www.citrusmassage.com', 'http://www.theheavenlyvegan.com', 'http://whasn.com/locations/whasn-centennial/', 'http://babymooninn.com/', None, 'http://www.unforgettablecoatings.com/', None, 'http://www.smileypies.com', '1592664595', 'https://www.caminodelsol.com', 'http://www.bigwavepoolservice.net', '1592664608', 'http://www.tropicalsmoothiecafe.com', None, None, 'https://www.hmv.ca/', '1592664625', None, 'http://www.twinoakslounge.com', 'http://www.steaksupreme.ca', None, None, 'http://www.sears.ca/', None, 'http://www.quiznos.ca', None, 'http://www.customcakesandtruffles.com', None, 'http://www.wendys.com/', 'http://www.manilakapamilya.com/', None, 'https://us.louisvuitton.com/eng-us/point-of-sale/usa/louis-vuitton-las-vegas-caesars-forum?utm_source=yelp&utm_medium=organic&utm_campaign=store_listing_storepage', 'http://www.tacobell.com', 'https://www.choicehotels.com/CN070?mc=blypypaf', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.quiktrip.com', 'http://www.fancofans.com', 'http://www.lowes.com', 'http://www.robertlynnhorne.com', 'http://www.russdarrowchryslerjeep.com/', 'http://www.civanacarefree.com/spa', 'http://www.pittsburghparks.org/park-features-3', 'http://www.PuraVidaVegas.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.primetimepaint.ca', 'http://www.arizonacenter.com/', 'http://www.phxfamilymed.com', 'https://www.walgreens.com/locator/walgreens-1654+n+pebble+creek+pkwy-goodyear-az-85395/id=12334', None, 'https://conferencecenteroflasvegas.com', 'http://goldenmaki.com/index.html', None, 'http://www.dunkindonuts.com', 'http://www.foodland.com', 'http://bcn-nv.com', None, 'https://agents.allstate.com/scott-feit-cottage-grove-wi.html', 'http://www.fibrenew.com/southhills/', 'http://xiangzihotpot.com', 'http://www.granditaliapizzavegas.com', 'http://bvbglass.com', 'http://www.birdcages4less.com', '1592664784', 'https://www.phoenixdogbutler.com', None, None, 'http://www.winnelectricllc.com', 'http://locations.daltile.com/nv/las-vegas/391', 'http://www.museindependent.tumblr.com', 'http://www.tcrsportlab.com', 'http://www.goodorthodontics.com', None, '1592664814', 'http://www.mattsbigbreakfast.com/', None, None, None, 'http://www.waddellsmusic.com/', None, 'http://www.facadelashes.com', None, 'http://bodyrocksdfs.com/', 'http://www.irg168.com/locations.html', 'http://www.littleheartsccc.com', 'https://ymcagta.org/find-a-y/mississauga-burnhamthorpe-rd-ymca-centre', 'http://www.rotigalore.ca', 'http://www.weplaycafe.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://salonblissful.com', None, 'http://www.hotdogonastick.com', 'https://boneyardbarbeq.com', 'http://www.matthewsmovingsystems.com', 'http://www.canopi.com', 'http://www.advancedeyecarevs.com', None, None, 'http://ville.montreal.qc.ca/portal/page?sc=5&_pageid=7377%2C94551572&id=74&_dad=portal&_schema=PORTAL', 'http://www.mark-taylor.com/arizona/the-reserve/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.bushschicken.com', 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', 'http://www.snappersfish.com/', 'http://locations.atipt.com/mesa-az-country-club-dr', 'http://www.sukiyakihouse.com/', 'http://cuplux.com', None, 'http://www.cashamerica.com/SUPERPAWN-stores/AZ/PHOENIX/Peo01', 'http://www.pariscocafe.ca', None, 'http://hiltongardeninn3.hilton.com/en/hotels/ohio/hilton-garden-inn-cleveland-twinsburg-CLETHGI/index.html?SEO_id=YELP-GI-CLETHGI', 'http://www.floors4youaz.com/', 'http://www.carowinds.com', 'http://www.camhplv.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://mcchgroup.com/dvino-home', 'http://www.provigo.ca/fr_CA/storedetail.2019.html', 'https://nationwidevision.com/locations', 'http://www.bemydd.com', 'http://www.salathaigoodyear.com/', None, None, 'http://www.relentlesschurch.tv', None, 'http://www.arcadiancle.com', 'http://www.papajohns.com/', '1592664996', 'http://www.flamingofloral.com', None, None, None, '1592665012', 'http://www.lsskincafe.com', None, 'http://www.marybrowns.com/', '1592665028', 'http://www.tullyscoffeeshops.com', None, None, 'https://www.skipsspringservicelv.com', 'http://www.oldworldbrewery.com', None, None, 'https://www.porschepittsburgh.com', 'http://www.shopbiltmore.com/union', None, 'http://nutrishoplasvegas.com/', None, 'http://pixel1530.everesttech.net/1530/r/56/73f3ab609d99b7ac8a34cb950ac4f99e/url=http%3A//www.la-z-boy.com/', None, 'http://www.floweramacleveland.com/', 'http://theartofdemolition.com/', 'http://www.tnollc.com', 'http://www.worldtravelaccessinc.com', None, 'https://www.mintmarkmadison.com', 'http://www.1stpriorityinspections.com', 'https://www.autozone.com/locations/az/mesa/4155-e-main.html', 'https://www.victoriassecret.com/store-locator#/store/1459', 'https://invisibleinktattooremovers.com/locations/tattoo-removal-pittsburgh/', 'http://www.creamistry.com', 'http://www.burntwoodtavern.com/burntwood-tavern-brecksville/', 'http://www.guyspizzaco.com/locations/chardon/', None, 'http://www.redmountaintire.com', None, 'https://www.solitudeatcentennial.com/?utm_medium=Listing&utm_source=Yelp', None, 'http://www.abcmotorcredit.com', 'http://gostreamlinemoving.com', None, 'http://www.livingroomrestaurant.ca', None, None, 'http://www.tacoslv.com/', None, 'http://www.threeoceansentertainment.com', 'http://www.inntopets.com', 'http://www.tindolford.com', 'https://sweetthrills.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.greatclips.com/', None, 'http://expressautoservicetire.com', 'http://stlouiswings.com', 'https://www.ymcacalgary.org/program-descriptions/locations/shawnessy/', None, None, 'http://www.foxxyladyscupcakes.com/', 'http://eatprepd.com', 'https://agents.farmers.com/az/glendale/jim-mckenna?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.firesidebookshop.com', None, 'https://www.papersource.com/locations/wi_madison_hilldale.html', 'http://www.cocoosteria.com', 'http://www.cinnamongirlclinic.ca/', '1592665232', 'http://www.queenofmaids.com', 'http://www.petkingdomusa.com', 'https://www.sprouts.com/stores/details/-/store-details/view/store/501/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://cask63.com', 'https://www.hardees.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.steelesyongeanimalhospital.ca/', 'http://homefurgood.org/', 'https://www.kfc.ca//store/7161-goreway-dr--kfc-tb-mississauga', 'http://www.azrain.org', 'http://www.sanagansmeatlocker.com', 'http://www.brenthalldds.com', 'https://www.statefarm.com/agent/US/NV/Las-Vegas/Matt-Keim-Z4K081YS000', 'http://beachwoodalbionapts.com', 'http://www.paramedicalskinhealth.com/', None, 'http://www.ChateauGems.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'http://www.leragazzeaz.com', 'http://www.warringtontire.com', 'http://www.rawlicious.ca', 'http://www.thecorndogco.com', None, '1592665314', None, 'http://amaranthfoods.ca', 'https://www.justsavefoods.com', 'http://www.courtesydental.com', 'http://www.kaliyana.com/', 'http://www.alpineairforce.com', 'http://www.belledeprovence.com/index.htm', 'https://www.wellsfargo.com', 'http://www.ncmilitarystore.com', 'http://www.creepycrawlypestcontrol.com', 'http://www.ferguson.com/branch/n-seventh-st-phoenix-az-plumbing', 'http://www.cultivate48.com', None, 'http://chase.com', 'http://www.twwevents.com', None, 'https://ad.doubleclick.net/ddm/clk/287230759;114269987;z?cvo_cid=8405710&http:%2F%2Faria.com%2Fdining%2Frestaurants%2Fbarmasa%3Fdfaid=1&cvo_adid=287230759&cvosrc=display.1375608.%C3%ACid%21&cvo_crid=%C3%ACid&cvo_pid=114269987', 'https://www.cellairis.com/store-locator', 'http://theburritofactoryclt.com', 'http://www.cmg-hoa.com', 'https://thebarbershoplv.com', None, 'http://www.kencars.com', '1592665400', None, 'https://www.mark-taylor.com/nevada/allegro/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://zipcityusa.com', 'http://drfransontom.com', 'http://www.style-encore.com', '1592665420', 'http://www.madamethai.ca', '1592665430', None, 'http://www.perryparklanes.com', 'https://lawreed.com', 'https://www.conalmapgh.com', 'http://www.infinitycloset.ca', 'http://www.landwer.ca', 'http://www.atastyaffair.net', 'https://www.walgreens.com/locator/walgreens-6601+mckee+rd-madison-wi-53719/id=5233', None, None, None, None, None, 'http://www.coppacoffeeandtea.com', None, None, 'http://www.cineplex.com/Theatre/cineplex-cinemas-fairview-mall', 'http://putahandleonyourcandle.com', 'http://www.revitasize.ca', 'https://myhoneybakedstore.com/parma/8411', 'http://www.themenssalon.com', None, None, 'http://www.tobaccotradercigars.com/grid', None, None, 'http://www.ejsushi.com', 'http://hiltongardeninn3.hilton.com/en/hotels/ohio/hilton-garden-inn-cleveland-airport-CLEAHGI/index.html?SEO_id=YELP-GI-CLEAHGI', None, None, 'http://www.greatamericannightmare.com', 'http://www.greatcarsandtrucksaz.com', 'http://www.woodcraft.com/stores/504/woodcraft-of-madison.aspx', None, 'http://www.hadlockrolfing.com', None, 'http://charlotteproperty.com', None, 'http://www.celestial-comics.com', 'http://www.asianlegend.ca', None, None, None, 'http://www.verdedimoraapartments.com', 'http://www.desertvolkswagen.com/', None, None, None, 'http://www.forthrightfunding.com', 'http://gunsplusaz.com', None, 'http://www.artisancolourspa.com', 'http://collinscleaners.com', 'http://www.dunkindonuts.com', 'http://www.tinocoskitchen.com/', 'http://thisendup.ca/', 'http://mommas-place.business.site', '1592665631', 'http://www.greatclips.com/salons/6330', 'http://www.georgios635wigs.ca', 'http://www.inspectonthemoney.com', None, 'https://blackbeardiner.com/location/henderson/', 'https://www.regmovies.com/theatres/regal-phillips-place/1877?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Phillips+Place', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.mycargurunow.com', None, 'http://l.macys.com/gilbert-az?cm_mmc=Yelp_Stores-_-Gilbert-_-n-_-465&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Gilbert_465&m_ac=yelp_stores&m_ag=n', 'https://jfairandheat.com', 'http://azmautomotive.com', 'http://elcharrohipster.com', 'http://www.pizzaranch.com/menus/4665_VERONA', 'https://www.thepointapt.com', 'http://antoniospizza.net', None, 'http://www.greentreechiropractic.com/', '1592665702', 'https://www.poop911.com/service-area/nevada/las-vegas-area/', 'http://www.zannamajerle.com', 'http://www.azclc.com', None, None, 'https://www.firkinpubs.com/firkinonthebay/', 'http://www.dontortaco.com/', 'http://palmvalleyoral.com/', 'http://www.elegantdentistry.com', None, 'https://www.slyfoxbeer.com', 'http://www.paintmyplace.com', 'http://www.phxcmc.com', None, None, 'http://www.gianteagle.com/Stores/Store/?storeId=4', None, None, 'https://www.amazinglashstudio.com/studios/pa/robinson-township/robinson-township', 'http://www.missdaisyflowers.com', 'http://www.barbiesgrill.com', None, '1592665775', 'https://fieldstone-technologies.ueniweb.com', None, None, 'http://www.lvfilmfest.com', 'http://www.nickysthaikitchen.com', 'http://www.clubcontroversy.com', 'http://sammydsdiscountarms.com', 'http://hopgoodsfoodliner.com/', None, 'http://www.carpetcleaninggilbertarizona.com', 'http://www.bk.com', None, 'http://www.manzettistavern.com', 'http://www.onetencafe.com', None, 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.hendryhomemortgage.com', 'http://www.gbpdsmiles.com', 'http://www.dcisalvage.com', 'http://Tonymedina.c21.com', 'http://www.skinupgrades.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.searshomeapplianceshowroom.com/locations/monroeville-pa', 'http://www.stonehavenremodeling.com', None, 'http://www.icedforlife.com/', 'https://locations.theupsstore.com/az/glendale/20118-n-67th-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.lookseyebrowthreading.ca', 'http://www.nationaldrivingschoollv.com', 'http://appliancerepairmadisonwi.com/', 'https://www.carstar.com/locations/oh/brunswick-15235/', 'https://www.themonitoringcenter.com', 'http://www.markhamhealthnetwork.com', 'http://www.allaccessvip.com/', 'http://www.ntb.com/store/8538/willoughby-hills-oh-44092-2786?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'http://www.associans.com', None, 'http://nailsense.ca/book', 'http://www.petitemaisonmtl.com/', 'http://joesjeans.com/', 'http://www.sushistar.ca/', 'http://www.ALittleMoreInteresting.com', None, 'http://cutting-edge-hair-salon-beauty-salon.business.site', 'http://www.hunsingerapts.com', '1592665955', 'http://www.pamier-kabob.com/', 'http://www.homehardware.ca', '1592665966', None, 'http://www.gartmanmodelbakery.com/', 'https://www.idealimage.com/medspa-locations/arizona/phoenix-area/phoenixpeoriaglendale', 'https://dealer.sprint.com/experts-choice', 'https://houseofthriftllc.wixsite.com/hotstuff', None, 'http://www.littlecaesars.com', 'https://www.mywaystorage.com/locations/pittsburgh-moving-pod-portable-containers/', 'http://www.suedeaz.com', 'http://www.eyebrowsrus.com', 'http://www.wetalkplants.com', 'http://www.bcbg.com', 'https://www.strikeforceservice.com', 'http://www.56kitchen.com', '1592666024', 'http://www.stellasdineinn.com', 'https://protechautogroup.com', None, '1592666039', '1592666043', 'https://www.rcwilley.com/location/Nevada/Las-Vegas-Summerlin-Nevada-Furniture-Store?utm_source=yelp&utm_medium=referral', 'https://www.lasvegastrailerrepair.com', 'http://amigoconstructionlv.com', 'http://brownroadfm.com', 'http://www.labriolaitalianmarkets.com', 'http://www.PrincessDentistry.com', '1592666069', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=38', 'https://www.walgreens.com/locator/walgreens-1159+e+southern+ave-mesa-az-85204/id=3670', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.azpedicab.com', 'https://www.wyndhamhotels.com/hotel/12522?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:12522', None, 'http://www.bamiyankabob.com/afghani-restaurant-locations/afghani-restaurant-maple/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://fabutan.com/locations/ontario/mississauga/applewood/', None, None, 'http://www.suckerscandyco.com', 'http://www.fitforlifetrainingofnevada.com', None, 'http://www.amcorprop.com', None, 'https://www.kohls.com/stores/il/champaign-126.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', None, 'http://www.fishwindowcleaning.com', None, 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store321', 'http://www.lasenza.ca', 'http://www.pizzabellagio.com/', 'http://www.westernsignsaz.com', None, 'http://42saint.com', 'https://www.jiffylube.com/locations/az/phoenix/2098', 'https://www.gsa.gov/portal/content/103451', 'http://www.linsrestaurant.com', '1592666159', None, None, None, None, 'http://www.cinemasguzzo.com/1-cinemas-schedules-mega-plex-taschereau-18-imax-.html#prettyPhoto', None, 'https://agents.allstate.com/william-duran-las-vegas-nv-1673738.html', '1592666179', 'http://www.rayspizzahappyvalley.com', 'http://livelaughphotography.com', 'http://www.starbucks.com/store/9334/', 'http://www.autoality.com', None, 'http://www.learninggardens.com', 'http://www.phoenixmidwife.com/', None, None, None, 'http://www.thegritty.com', 'http://www.vivanapolipizza.com/', None, 'http://www.redhousefamilyrestaurant.com', None, None, 'https://privityboutique.com', 'http://www.gracespacechristiancoaching.com', 'https://www.wyndhamhotels.com/hotel/15427?tel=18002521709&iata=00093785&cid=fe:ra:20161215:yl:pp:ramus:15427', 'https://www.nomadlasvegas.com/en.html', 'https://azlawyer.net', None, '1592666259', 'http://www.ricrec.com', 'http://www.lombardopools.com', 'http://www.dwr.com/category/find+a+studio/scottsdale.do?mobile=off', None, 'http://www.hpspecialists.com', 'http://www.madisontailor.com', 'http://1890blowdrybar.com/', 'https://arizonabusinesslawyeraz.com', 'http://www.myglt.net', 'http://www.terancefloydstudios.com', None, 'http://www.thephoenician.com/il-terrazzo/', 'http://crumbleslv.com', 'http://www.templebnaitikvah.org/', 'https://www.cashmoney.ca/find-a-store/ontario/toronto/yonge-and-bloor', 'https://www.bankofamerica.com', 'http://www.memoriesbykaren.com', 'http://metrodentalcenter.com', 'http://www.cooln2canada.com', None, 'https://www.gohealthuc.com/north-carolina/charlotte/waverly?utm_source=yelp&utm_medium=referral&utm_campaign=yelp%7Clistings%7C2020-nc-null-novant-011520-waverly', 'https://www.skyharborairportparking.net', None, None, 'http://www.holtrenfrew.com', None, 'http://www.dealerschoicedetail.com', 'http://www.sharpshineauto.com', None, 'http://www.newvistasaz.com', None, 'http://www.cjay92.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.firepowerrange.com', 'http://wingwarehouse.com', 'http://www.2ndsole.com', 'https://www.floatology.com', 'http://divaspaandnails.com', 'https://www.ashleyfurniturehomestore.com/furniture-stores/united-states/il/champaign/champaign?cmpid=2016YELP', 'http://www.ruelo.com/', 'http://www.calibercleaning.com', None, 'http://www.crepedelicious.com', 'https://www.metro.ca/en/find-a-grocery/320', None, 'http://www.candiesautodetailing.com', 'http://local.firestonecompleteautocare.com/north-carolina/charlotte/5340-e-independence-blvd/?lw_cmp=IYP_YPC_MLP_10790', 'http://sichuan-kungfu-fishrichmondhill.business.site', 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', None, 'https://sackssandwiches.com/sacks-hardy/', None, 'https://expansiveviewlandscape.com', 'https://www.take5oilchange.com/locations/oh/stow-154/', None, 'https://deja-brew-unforgettably-great-coffee.business.site', '1592672127', None, 'https://burgers2beer.com/location/lakewood/', None, 'http://www.quiktrip.com/', 'http://ryanautomotive.biz/tires-auto-repair-crafton-pa', 'http://www.eastsidecutterslv.com', 'http://www.absolute-offroad.com', 'http://www.pioneertablepads.com', 'http://420gawds.com', 'http://www.vesthetics.com', 'http://www.originalroccosfamousphilly.com', 'http://www.mamieclafoutis.com/van-horne', 'http://www.bayarts.net', None, None, 'http://stevescafeaz.com/', 'http://www.airspeedmechanical.com', 'http://cjspubnc.com/home.html', 'http://www.sharis50sdiner.com/', 'http://www.goodwillsp.org/shop/retail-stores/pineville/', 'http://www.petmedicalcenter.com/', 'https://www.goldencorral.com/locations/2701/golden-corral-w-sunset-road/', 'https://www.gopartydecor.com', 'http://www.pelliniitalian.com', 'http://www1.shoppersdrugmart.ca/en/store-locator/store/774', 'https://sprayvalet.com', 'http://www.sarkujapan.com', 'https://www.frysfood.com/stores/details/660/00055', 'http://www.resyslv.com', 'http://www.barrymorelive.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, None, 'https://www.cosmopolitanlasvegas.com/restaurants?utm_source=yelp&utm_medium=organic&utm_campaign=yelp', 'http://qnailsalon.ca', 'http://www.regalnails.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.verizonwireless.com/stores/pennsylvania/homestead/the-waterfront-284515/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.sausageshoppe.com/', 'http://www.cadillacjenkins.com', 'http://www.wholefoodsmarket.com/stores/charlotte', 'http://www.puedmaginkpire.com', 'https://evergreen-tobacco.business.site', 'http://www.starbucks.com', None, None, '1592672297', None, 'https://www.kaltire.com/en/stores/locations/?source=yelp_track&StoreID=866', 'http://www.azapartmentoptions.com/', 'http://www.thomasvilleaz.com', 'https://santanbrewing.com', 'http://www.thehangarmuseum.ca', None, 'https://www.officedepot.com/storelocator/az/scottsdale/officemax-6188/', 'http://www.sweetjesus4life.com/', 'http://www.frysfood.com', 'http://www.alpineinsurance.ca', 'http://attorneyneedham.com/', 'https://www.mississaugacosmeticsurgeryclinic.com/mississauga-location.cfm', 'http://www.bridalspectacular.com', 'http://www.theharmonyhouse.com/', 'http://www.palmettoskincenter.com', 'http://waxingbyann.com', 'https://www.scenic.com/tours/las-vegas/?utm_source=yelp&utm_medium=citation&utm_campaign=2020_citations&utm_content=boulder_city', None, None, 'https://www.walmaneye.com', None, 'https://www.pteglv.com/locations/pts-gold/st-rose-eastern/', 'http://www.flashonchurch.com', 'http://www.nohohontea.com', '1592672388', None, 'https://www.gasolinestreetcoffee.com', 'http://www.evrc.net', 'http://www.alexandersfloraldesigns.com', 'http://moldovarestaurant.com', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB140&Entt=RDMLIB140', 'http://losfavs.com', '1592672415', None, None, 'http://www.modoyogabloorwest.com', 'http://www.poochiesparadise.ca', 'http://www.virtualofficeslv.com', None, 'http://redrockah.com', None, 'https://www.sunterramarket.com/Locations/Gulf%20Canada%20Square', 'http://www.novusaz.com', 'http://www.peterbarach.com', 'http://www.igifoods.com', None, None, 'http://yimeichampion.com', None, 'http://www.shoelessjoes.ca/', 'http://popeyes.com', 'http://www.lazeezshawarma.com', 'https://uniquerestoration.us', 'https://www.glenoaksisyourhome.com/glen-oaks-apartments-glendale-az', 'http://www.nofrills.ca/en_CA/storedetail.334.html', 'http://neighborhoodlender.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZAL', 'https://www.merrillgardens.com/senior-living/az/gilbert/the-oaks-a-merrill-gardens-community', 'http://www.starbucks.com/store/9334/', 'http://www.mybutterflyspa.com/', None, 'http://www.rappoptical.ca/', 'http://www.jim-dickerson.com', 'http://michaelhoban.cbintouch.com', 'http://www.wetseal.com', 'https://www.wyndhamhotels.com/hotel/30805?tel=18882935571&iata=00093785&cid=fe:bh:20161215:yl:pp:hawus:30805', 'http://www.kporterinsurance.com?cmpid=BW6W_BLM_0006', 'https://www.wyndhamhotels.com/hotel/07836?tel=18006817991&iata=00093785&cid=fe:ra:20170223:yl:pp:ramca:07836', 'http://www.hanger.com/', 'http://www.lush.ca', 'http://www.giosmeats.com', 'http://platinumhairbar.com', 'http://drjeanlouis.com/', 'http://www.mountsinai.on.ca', 'http://www.bk.com', None, None, 'http://www.cookout.com', 'http://www.easydrinkeasygo.com', 'http://www.arbys.com/', None, None, None, None, 'http://chhuystempe.business.site', 'http://www.kachinaapartments.com', None, 'http://www.rubinsfurniture.com', 'http://paulenesnailspa.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.munchkinspreschool.com', 'http://matrixdentistry.com', 'https://foxandfiddle.com/locations/fox-on-york-mills', 'http://www.sonnysboxinggym.com', 'http://diamonddryclean.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.bladerunnersbarbernsalon.com', None, 'http://www.drruggeri.com/', 'http://www.quiktrip.com', None, 'https://madisonwest.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.osbi.org', 'http://nailsbygaylee.wordpress.com/', 'https://local.fedex.com/az/scottsdale/office-2256/', 'http://www.eki-bento.com', 'http://www.speedyglass.ca/locations/Calgary-Center', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://www.districtdental.ca', 'http://www.hundredwood.com', 'http://www.h4uconstruction.com', None, None, 'https://www.cactusweddingfilms.com', 'http://www.fantasiacrystals.com/shop', None, 'http://stevekader.wixsite.com/lasvegaspartytours', 'http://www.filibertos.com', 'http://www.comicsarego.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://calstate.aaa.com/?=yelp_track', None, 'http://www.blindpigco.com', None, 'http://www.sanbellinoapts.com', 'https://palmbeachtan.com/locations/NC/Huntersville-Northcross-Center-Court/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=AUG', None, 'http://fallspaknship.com', None, 'http://www.olsonrollingshutters.com', 'http://homehardware.ca', 'https://www.neweyeslasvegas.com', None, '1592672784', None, None, None, 'http://makdeli.com/', 'https://www.shopthehouse.com', 'http://nevadahomefitness.com', None, 'http://lunarossaristorante.com/', 'https://www.meineke.com/locations/az/peoria-1593/?utm_source=yelp&utm_medium=xvc', None, 'http://www.stewartdetailing.com', 'http://www.dentalbrothers.com', None, 'http://eatatverde.com', 'http://www.audiocommunications.com', None, 'http://sevabeauty.com/location/phoenix_az_35th-avenue', 'http://www.einsteinbros.com/', 'http://www.arizonaorthopedicsurgeons.com/about/randall-hardison-md', None, None, 'https://www.mysodalicious.com', 'https://www.ttc.ca/Subway/Stations/Scarborough_Centre/station.jsp', None, '1592672860', 'http://www.twistedcoilvapes.ca', 'http://www.moonvalleychiropractic.com', 'http://locations.saksoff5th.com/en/las-vegas-south', 'http://www.arrowheadmb.com', 'http://www.dlsouthwest.com', None, 'http://www.united-rv.com', None, None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.masterwatchrepair.com/', 'https://www.batteriesplus.com/store-locator/az/phoenix/batteries-plus-332?utm_source=yelp&utm_medium=local&storecode=332', None, 'https://www.mypersonaltrainerwestlake.com', None, None, None, None, None, 'http://www.destinationmaternity.com/', 'http://www.lasvegasluvbugweddings.com', 'http://www.radatattattoo.com', None, None, 'http://www.juliosaz.com/', 'http://www.punkasspiercingsink.ca/', 'http://www.bluebrotherspools.com', 'http://www.buckle.com', 'http://www.myplazabonita.com', None, None, 'https://www.anytimefitness.com/gyms/141/Madison-AL-35758/?utm_source=yelp&utm_medium=local', 'http://www.pizzahut.com/', 'http://www.thehickorytavern.com/', 'http://dimaggios.fcvmobile.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.heidioptics.com', 'http://www.starbucks.com/store/15887/', None, 'http://www.landmarkcinemas.com/en.aspx', 'http://www.buddhasbazaar.com', 'https://www.abrazohealth.com/our-locations/abrazo-arrowhead-campus', 'http://www.patsdrycleanersaz.com', None, 'https://www.westerndental.com/en-us/find-a-location/arizona/tempe/1080-w-elliot-rd', 'http://www.starbarksaz.com', None, 'http://peopleseatery.com/', 'http://www.joemaggianos.ca', 'https://stores.jcpenney.com/az/phoenix/salon-phoenix-az-1480.html', 'http://reunionislandcoffee.com', '1592673048', '1592673052', None, None, None, 'http://www.fredastaire.com/ahwatukee', None, 'http://blindbeggarpub.com/', None, None, 'http://www.lasvegasfootandankle.com/', 'http://www.pitaland.ca', 'https://www.ulta.com/stores/pittsburgh-pa-1177', None, 'http://www.vokitchenandbar.ca', 'https://www.cash1loans.com/locations/arizona/phoenix-thomas.aspx', None, 'http://www.sarawatermanphotography.com', None, None, None, 'http://www.mayfairclubs.com', 'http://www.jasperdentistry.com', None, 'http://www.aptselector.com/phoenix', None, 'http://quattro4ragazze.com/', None, 'http://www.gamestop.com', 'https://movesmartmoving.com/', 'http://tirediscountparma.com', 'http://shopdaystar.com', 'http://www.rivierarvpark.com', '1592673161', 'http://www.tacoshuevos.com', 'http://www.jesuisunenfantterrible.com/laval/', 'http://www.chanostowingaz.com', None, None, None, '1592673185', 'http://ghgreenspringspa.com/', 'http://stores.newbalance.com', 'https://www.mitroteam.com/beth-mitro-bio', 'http://los-armandos.business.site', 'http://leesatamember.com/locations/laveen/', 'https://www.sweye.com/locations/scottsdale-miller-rd/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-scottsdalesouth&utm_content=website', 'https://www.ihop.com/en/restaurants-phoenix-az/5020-e-ray-rd-1508', 'https://stores.dickssportinggoods.com/az/gilbert/363/', 'http://www.dentalstudio101.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/19305+West+Catawba+Avenue-Cornelius-NC-28031/storeid=2314?cid=ps_ylp_2020', 'http://www.precisiondentalaz.com', 'http://www.paradisepictureframe.com', 'http://www.goodwillgoodskills.org/contact-us/find-a-location/mayfield-heights.aspx', None, None, None, None, 'http://www.neuroazcenter.com', 'https://www.precisionautomotiverepairs.com', None, 'http://storelocator.pepboys.com/pepboys/stores/scottsdale/scottsdale/00684', '1592673265', 'http://www.portofsubs.com', 'https://www.larrymillergenesis.com', 'http://www.butchharmon.com', None, None, None, 'http://www.continentalcleanersaz.com', 'http://www.urbanabusiness.com/Sweetcorn_2007/Sweetcorn_2007.html', 'http://www.synergyalarms.net', 'http://www.greencartires.com', 'http://www.freshstartcoffeeco.com', 'http://www.ljsilvers.com', None, None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZCC', None, None, 'http://www.pittsburghjuicecompany.com/', 'https://www.carstar.com/locations/oh/euclid-15070/', 'http://www.nextrelic.com', 'http://www.aztangibletanning.com/', 'http://lagourmandinebakery.com', 'https://order.loumalnatis.com/store_menu/47?utm_source=Yelp_phoenix', 'http://someburros.com/', 'http://www.soulcutheatwave.com/', 'https://stores.dickssportinggoods.com/pa/pittsburgh/42/', None, 'https://www.integrativerheumatology.org', None, 'http://www.sistersisterbraiding.com', 'http://www.theschombergpub.com/', 'http://ceturylink.com', 'http://www.riverranchapts.com/', None, 'https://www.hilton.com/en/hotels/cledrhx-hampton-cleveland-westlake/?SEO_id=YELP-HP-CLEDRHX', 'https://www.carx.com/champaign/2216-s-neil-st/', 'http://myluminescence.com', 'https://www.aceno3.com', None, 'http://www.babesinarms.ca/', 'http://www.rockyrivertrading.com', 'https://www.bobevans.com/our-restaurants/locations/98?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://mrgreek.com/mrgreek.com/bathurst', 'https://www.bravoitalian.com/henderson.html', None, 'https://www.charlotteunitedcab.com', 'https://pinehurstonprovidence.com', 'http://www.kimmyzongreenway.com', 'http://www.themissionchapel.com', None, 'https://www.spacesworks.com/scottsdale/old-town-galleria/?utm_medium=portal&utm_source=YelpUS', 'http://www.hairofthedogaz.com/contact.php', 'http://www.abyssiniatoronto.com', None, None, None, None, 'https://www.federalgalley.org/restaurants/which-came-first/', 'http://powerwindowrepair.com', None, 'http://www.teamlogicit.com', None, 'http://Zales.com', None, 'http://universityobgyn.net/index.cfm?pID=6968', 'http://www.taigunoodles.com', 'http://luxesalonspaaz.com/', 'http://domainedelatemplerie.com/app/', 'http://www.aocphysicians.com/locations/phoenix-office', 'http://www.azbone.com', None, 'http://robeks.com/locations/strongsville-oh.html', 'http://www.east-sideautomotive.com', 'http://stone-oven.com', None, 'http://regalcatcafe.com', 'http://www.thefacialplace.com', None, 'https://www.arizonatile.com/en/locations/glendale', None, '1592673557', None, None, None, 'http://www.dirtyharrys.net', 'http://www.ice-performance.com', 'https://www.wellsfargo.com', 'http://www.gymboree.com', 'http://www.cyberknifeoflasvegas.com', 'https://stores.hallmark.com/az/phoenix/stacys-hallmark-shop-phoenix-az-17308.html', 'http://www.mountpleasantgroup.com/pre-planning/cemeteries/properties/n', 'https://stores.sportsmans.com/sportsmans-warehouse/us/az/phoenix/19205-n-27th-avenue', 'https://www.maxstoragelv.com', 'https://www.umamiburger.com/locations/nv/las-vegas/', 'http://www.estheticsbyamber.com', None, 'http://www.bellaroseestate.com', 'http://www.buttermilkfinewaffles.com', None, 'http://www.teslamotors.com', 'http://www.colonialprop.com/Apartments/module/property_info/property[id]/22821/', 'https://ad.doubleclick.net/ddm/clk/434331165;236814625;c', 'http://www.timhortons.com/', None, 'http://www.highsocietyboutique.com', 'http://www.shell.com/', None, 'http://www.liquordepot.ca/?utm_source=Yelp&utm_medium=Online_Listings&utm_content=Location&utm_campaign=LiquorDepot_AB_Q3_July_September_2017', 'http://www.yogisgrill.net', 'http://www.hamadsautorepair.com', 'http://www.islandnailsandspa.com', None, None, None, None, 'http://www.ihop.com', None, 'http://fuelpizza.com', None, 'http://www.cleaningmill.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://www.starbucks.com/store/9298/', 'http://www.champps.com/', 'http://burlesquehall.com', None, 'http://www.whypayalawyer.com', None, 'http://ganleylincoln.net', 'http://www.irs.gov', 'http://www.soma.com/store/home.jsp?cmp=MOC_yelp', 'http://www.ccfoxrealty.com', 'http://nextcoffeecompany.com', 'http://www.hazelfreshcc.com', 'http://www.powersstainedglass.com/', 'http://www.eglintonstationmedical.ca', 'http://www.greenockfarm.com', None, 'http://www.z-teca.com', '1592673772', 'https://www.pewlaw.com', 'https://affordableazdivorce.com', None, 'http://www.eastlandmall.com', 'http://www.sellingrestaurants.com', None, 'http://www.phoenixvapelounge.com', '1592673802', None, 'http://www.bouncehousephoenixaz.com/', 'http://lasvegas.jiffylube.com/Locations/Store/1975/4531-N-RANCHO-RD-LAS-VEGAS-NV-89130-3403', 'http://www.barvolo.com', 'http://www.pizzanova.com', 'http://stripperking.com/', 'https://tocayaorganica.com', 'http://www.completespray.com', 'http://www.larymdesign.com', None, None, 'http://www.boosterjuice.com', 'http://www.boulangeriejaura.ca', 'http://www.miraclepoolcare.com', None, 'http://CogburnCares.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', None, 'http://www.bsrauto.com/', 'http://www.suntechair.com/home.html', 'http://portofsubs.com', 'http://abundanthealthaz.com', 'http://www.discountnutritionsuperstore.com', 'http://www.filibertos.com', 'http://cogscycle.com/', 'http://www.traderjoes.com', 'http://Werundacut.ca', 'http://www.louisaleash.com', 'http://arizonapaintreatmentcenters.com/', 'http://www.piperglenanimalhospital.com', 'https://www.cricketwireless.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://19thavegarage.com', 'http://www.MovingAtEase.com', None, 'http://air-care.com', '1592673945', 'http://www.fiorio.com/', None, None, 'http://www.jcsu.edu', 'http://www.hottiesworld.com', 'https://www.slumberland.com/stores/-j6-champaign-il', 'https://bostonpizza.com/en', None, None, 'https://orthodontistofhenderson.com', 'https://www.publicstorage.com/california/self-storage-concord-ca/94520-self-storage/149?pid=wyelp&CID=1245&CHID=AFL', 'http://quinterojewelry.com', 'http://www.incaroofing.com', 'http://www.mpsaz.org/zaharis', None, 'http://www.myenvyhome.com', '1592674003', 'http://www.mcgsrollinworkshop.com', 'http://www.gianteagle.com', None, 'http://www.pageonecafe.com', 'https://www.marcostankless.com', 'http://markpi.com', 'http://thriftdlux.com/', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://candiescharacters.org', 'http://www.wdsarch.com', 'http://www.omahasteaks.com/stores', 'http://bigtextrailerworld.com/phoenix/?utm_source=Yelp&utm_medium=Directory&utm_campaign=Listing', 'http://www.vegassparkles.com', 'http://www.theamancan.com', None, 'https://www.waldorfastorialasvegas.com/dining/tea-lounge/', 'http://www.bluepointmedicalspa.com/', None, 'http://www.goldbythegrampawn.com', None, None, None, 'https://thehairstandard.com', 'http://www.cajun-daves.com/', None, None, 'http://www.sunglasshut.com/us/?cvosrc=display.yelp.LasVegas', 'http://www.9037salonlv.com', 'http://www.pizzafire.com', '1592674119', 'http://www.vegasatvadventures.com', 'http://www.toryburch.com', 'http://www.consigntoronto.com', 'http://www.arcadiawalk.com', None, None, 'https://www.pizzadiromamenu.com', None, None, 'http://local.biglots.com/az/tempe/4280', 'http://www.cdohd.com/', None, None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/2371+East+Guadalupe+Street-Gilbert-AZ-85234/storeid=3272?cid=ps_ylp_2020', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.aspensquare.com/apartments/nevada/las-vegas/millennium-east?utm_source=Yelp&utm_medium=Yelp', 'https://www.regissalons.com/locations/az/gilbert/regis-salon-val-vista-town-center-haircuts-1779.html', None, 'http://nathansfamous.com', 'http://www.phoenixcharlotte.com/', None, 'http://www.learningdynamicspreschool.com', 'http://www.ancientspaandboutique.com', 'http://www.sunglasshut.com/us', 'http://www.toronto.ca/animal_services/centres.htm', 'https://www.staples.com', 'http://theupsstore.ca/436/', 'http://www.kiplingtire.ca', 'http://www.econappliance.com', None, 'http://www.goldenspoon.com/', None, 'http://www.dineattheriver.com', 'http://www.knockouts.net/', 'http://www.ScottsdaleNights.com/', 'http://Soul2Sole.ca', 'https://rainbowintl.com/north-phoenix/', 'http://www.linex.com/?utm_source=yelp%2Bnational%2Bprogram&utm_medium=website%2Btraffic&utm_campaign=yelp%2Bbedliner%2Bsearch', 'http://www.meridiamedical.com', 'https://markherman.ca', 'http://www.cyclandscaping.com/', '1592674271', 'https://store.vioc.com/pa/pittsburgh/4469-ohio-river-blvd-15202-060069', None, None, None, None, 'http://www.topgunburgerto.com', '1592674299', '1592674305', 'http://www.huesalonandspa.com', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://www.thehandymannextdoor.com', None, 'http://www.tresses.ca', None, None, 'http://www.lakemeadfishingguide.com', None, 'http://Furkidsdaycare.ca', 'http://www.pastansugo.com', 'http://www.pristinepooltile.com/', 'https://locations.theupsstore.com/az/gilbert/70-s-val-vista-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://phoenixchildrens.org/locations/phoenix-childrens-pediatrics-dobson-village', 'http://vetonbathurst.com/', None, 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', 'https://www.pizzahut.ca/store-details/store-R32814/pizza-hut-Mississauga', 'http://www.pelicanssnoballs.com/', 'http://www.ribsnbread.com', None, 'http://www.kuhnsportandspine.com', None, 'https://www.goodshomefurnishings.com/furniturestores/charlottenorthcarolina', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sunglasshut.com/us/?cvosrc=display.yelp.LasVegas', 'https://www.nsbank.com/branch/?branch=durango_and_215_south_branch', 'http://comfortdental.com/dentist-west-mesa/', None, 'http://sierrabonitagrill.com', 'http://www.paulosardinhabbqchicken.ca', 'http://www.avonanimal.com', 'http://westspringsmedical.com', 'http://unioncountykia.com', 'https://farsidinein.com', None, None, 'http://www.absinc-sw.com', 'http://www.crescent-supply.com/', 'http://www.nachoria.com', 'http://www.lionheartbritishpub.com', '1592674472', 'https://www.extraspace.com/storage/facilities/us/arizona/peoria/900038/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://hairzzaplon.com', 'http://www.dominos.com', 'http://cleansolutionsoh.com', 'http://bellaskyn.com', 'https://www.thebrick.com/pages/store-calgary-sunridge', None, 'http://www.MiamiHypnosisCenter.com', 'http://beamcleaning.ca', 'https://www.walmart.com/store/1380/las-vegas-nm/details', None, None, 'https://www.allstateselfstorage.com/self-storage/tempe-85282', None, 'http://www.barlescousins.ca', 'https://www.nomadlasvegas.com/en.html', None, 'http://justtruckandvan.com', 'http://www.desertbreezeglass.com', 'http://pizza.dominos.ca/North-York-Ontario-10286', 'http://www.pivotphysicaltherapy.com/find-a-location/location-detail/downtown', 'http://cakesbymariaandjoe.com', 'http://www.ccanv.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://disappearinginkltr.com', 'http://www.ppgplace.com', 'https://www.dunnedwards.com/directory/store-list/phoenix-008', None, 'http://www.yogurtplusaz.com/', None, None, None, 'http://www.kevinsjunkremoval.com', None, 'http://smokesburritorie.com', 'http://www.shouldice.com', 'http://www.windownation.com/cleveland-showroom', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, None, 'http://rotundaelectric.com', 'http://www.ihop.com', 'http://www.lasvegasshutterco.com', 'https://www.officedepot.com/storelocator/nv/las-vegas/office-depot-3351/', 'https://www.timhortons.ca', 'http://www.lakeparktower.com', '1592674643', None, 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', 'http://www.gluuteny.com', None, 'http://crossroadsanhosp.com/', 'http://www.starbucks.com/store/9229/', 'https://www.redrobin.com', 'https://coughingcanary.net', None, 'https://asafiir-market-and-restaurant.jimdosite.com', 'http://www.lalookboutique.com', 'http://www.downwarddog.com', None, 'http://www.ccpc.ws/', 'http://draughtcharlotte.com', 'http://www.centralparksquareathletic.com/', 'https://www.hilton.com/en/hotels/lasgigi-hilton-garden-inn-las-vegas-strip-south/?SEO_id=YELP-GI-LASGIGI', 'http://www.Whitelilyfilms.com', 'http://www.nicetartes.com/', 'http://www.esurranty.com', '1592674724', None, 'https://buildingkidzschool.com/loc/az/chandler-preschool-infant-toddler-care/', 'http://www.outback.com/store.aspx?store=3630&utm_source=Goo&utm_medium=maplistings&utm_campaign=localmaps', 'http://www.bluedoorcalgary.com', 'http://soulfoodcafelv.com/', 'https://roadrunnerflorist.com', None, 'http://www.standrew-cfc.org/', None, 'https://local.safeway.com/safeway/az/goodyear/14175-w-indian-school-rd.html', 'http://spayme.com/', 'https://locations.wendys.com/united-states/oh/lorain/1410-colorado-ave', 'http://www.thelegacyballroom.com', 'http://www.holikaholika.ca/', None, 'http://www.desertendo.com/', 'https://www.kaltire.com/en/stores/locations/?source=yelp_track&StoreID=616', None, None, 'http://www.giuseppescottsdale.com/', 'https://www.tgifridays.com/locations/2580/fridays-madison-tennessee', 'http://www.mikehengy.com', 'https://www.tempurpedic.com/tempur-pedic-stores/tempur-pedic-southpark/', None, 'https://consumertire.com/tires-auto-repair-mentor-oh', 'http://Collisionworksmesa.com', None, 'http://www.furniturewithasoul.com/charlotte', None, None, 'http://wedion.com', '1592674835', None, None, None, 'http://www.buldogis.com', 'http://bendermattress.com', None, 'http://www.knickersnlace.net', None, 'http://www.alyourtreespal.com', 'https://www.samedaywater.com', None, 'http://www.healthwindsspas.com', 'http://www.lasvegasestatelaw.com', 'https://dbyoga.ca', 'https://www.shapesbrowbar.com/rmla---chandler-mall-inline/', 'https://www.shaneco.com/jewelry-stores/phoenix-az?cid=display&scid=yelp&cnid=evergreen&atid=phoenix-ga&campid=evergreen19utm_source=yelp&utm_medium=sNatural&utm_campaign=soc_yelp_sNat_evergreen19_storelink_phoenix', 'http://www.innerfireyoga.com', 'http://rnailsmatthews.com', 'https://eddieofalltrades.com', 'https://www.arslanianbros.com', None, 'http://www.primopaving.ca/', None, 'http://www.sylvieandshimmy.com', 'http://mrtsfireplaceservices.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', 'http://www.greatclips.com/', 'https://www.officedepot.com/storelocator/oh/solon/officemax-6589/', None, None, None, 'http://ironworksrestaurant.com', None, 'http://www.goodwillaz.org/', 'https://stores.hallmark.com/az/surprise/sarahs-hallmark-shop-surprise-az-65405.html', None, 'https://www.goodwillaz.org/location/arizona-ave-pecos/', None, None, 'http://www.moes.com', 'http://www.timhortons.com/', None, None, 'http://www.sherwin-williams.com/store-locator/paint-store/Las%20Vegas/NV/8114', None, 'http://www.bimslawn.com/', None, None, None, None, 'http://inspec10.com', 'http://www.sonicdrivein.com/', 'http://oncueinstalls.com', 'http://arizonadiamondcenter.com', 'http://www.casablancahookah.com/', 'https://c4.construction', None, 'http://www.bscmoto.com', 'http://www.popeyeschicken.ca/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.customistic.com', 'http://levieuxfour.net', 'http://www.qbrideandformals.com', None, None, 'http://alterations-express.com/find-us/?store_id=9', None, 'http://www.sushikeetempe.com', 'http://www.autozone.com', 'https://www.mikesswatteam.com', 'http://www.promakeupart.com', 'http://www.stylebysana.com', 'http://sunshinedoulaservices.com', None, 'http://Www.darkmoon.coffee', None, 'http://www.blairbbq.com/', 'http://agentlefarewell.com/', 'https://www.t-mobile.com/store-locator/nc/pineville/carolina-place-6?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://kaishosushiramenlasvegas.myrestaurantpage.website', 'http://redrock.clarkcountynv.gov/parksloc/details.aspx?park=91', 'http://www.autoglassexpress.com', 'http://www.grahamsbakery.info', 'http://whasn.com', 'https://www.leikinvolvocarscleveland.com', 'https://www.goodwillaz.org/location/61st-ave', 'http://www.planetbeach.com', 'http://www.thelittlegym.com/ballantyneNC', 'https://locations.wendys.com/canada/on/whitby/1-paisley-ct.', 'http://www.mbscottsdale.com', 'http://www.lunaclt.com', None, 'http://www.sculpturesupply.com', None, 'http://www.spacaladae.com', 'http://restorationcleanupnc.com', None, 'http://www.artisticpoolandspa.com', None, None, 'http://www.Wahlborgelectriccompany.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://daveharforddesign.com', 'https://www.mcilveenfamilylaw.com/north-carolina/charlotte', None, 'http://www.goddessbrowsandmicroblading.com', None, None, 'http://www.ssacafe.com/', None, None, 'http://www.latraviata.ca', None, None, None, None, 'https://milios.com', 'http://www.superiorskincarebylaura.com', 'https://locations.timhortons.com/ca/on/oakville/494-dundas-st-w.html', None, 'http://www.JimmyJohns.com', 'http://humberbayvethospital.ca/', 'http://www.relaxationz.com', 'http://www.azrainfall.com/', 'http://loloschickenandwaffles.com/location/scottsdale/', '1592675270', 'http://www.windautoglass.com', 'http://centurywellness.ca', 'http://www.wfcicdental.com', 'http://www.sincityburgers.com', None, '1592675292', 'https://blackfinnameripub.com/charlotte-uptown/', 'http://www.goodtasteofbritain.com', 'http://www.irstaxdoctor.com', 'http://www.tokyobeautystudio.com', 'http://www.jazzberryteahouse.com', 'http://www.rainbowroomsalon.com', 'http://www.teamfarnham.com', 'https://janies-homemade-hard-ice-cream.business.site', None, 'http://www.cmazier.com', 'http://www.saharacoins.com', 'http://www.dukesbread.com', 'http://www.petsmart.com', 'http://www.desertforrestnursery.com', 'http://www.adgairac.com', None, 'http://www.umisushiexpress.com/', 'http://www.harveysrestaurantandginbar.co.uk', None, None, 'http://www.woodys.com/home.html', 'http://www.maddiesonmadison.com', None, None, 'https://embassysuites3.hilton.com/en/hotels/north-carolina/embassy-suites-by-hilton-charlotte-ayrsley-CLTTBES/dining/index.html', 'http://www.rodsickler.com', 'http://www.BAChiropractic.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, 'https://stores.bestbuy.com/wi/madison/7357-w-towne-way-208.html/?loc=ns100&ref=NS', None, 'http://www.CraigBilliards.com', 'http://www.edgemontvet.ca', None, 'http://www.kensington-market.ca', 'http://www.lasvegaslocksmithservices.com', None, 'https://stores.bestbuy.com/az/mesa/6315-e-southern-ave-254.html/?loc=ns100&ref=NS', 'https://www.flynnstire.com', 'http://www.bodyvision.com', 'http://www.dominos.com', 'http://www.boltinilounge.com/', None, 'http://www.canadadiagnostics.ca/', None, 'http://burlesquehall.com', 'http://www.frescomadison.com', 'http://www.laserclinics.com', 'http://www.camdenspa.com/', 'http://www.culliganwater.com/locations/az-phoenix', None, 'http://www.dunkindonuts.com', 'https://gymvmt.com/clubs/north-hill/', 'http://www.queencreekolivemill.com', None, None, 'http://umisushiexpress.com', 'http://www.dominos.com', 'http://www.studentbookcenter.com', None, None, 'http://name-brand-exchange.com', 'http://www.automoves.ca', 'http://www.wedding-alterations.com', 'http://www.jojoesautomotive.com', 'http://www.lilacmassagelv.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://lulusnails.wix.com/lulusnails', 'http://solutionsshutters.com', 'http://www.kirby.com', 'http://www.citycleaner.com', None, None, 'http://www.michaelshew.com', 'http://www.getyoursource.com', None, 'http://www.bridalelegance.com', 'http://andersonroofingandrepair.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.drwolnik.com', None, None, 'http://tempocharlotte.com', 'http://www.redsplacetwinsburg.com', 'http://www.sincitysalseros.net', 'http://www.acehardware.com/store-details/10341', 'http://www.torylcooper.com/', None, 'http://lamolisanacafe.ca/', None, 'http://www.rackroomshoes.com', 'http://www.wingstop.com', None, '1592677987', 'http://www.completepigeoncontrol.com', 'https://www.bankofamerica.com', None, None, 'http://mollyspilates.com', 'http://www.moonparks.org/moonparks/robinhill.html', None, 'http://www.shapesbrowbar.com/', 'http://esnail.co', 'https://www.911restorationmesa.com', None, None, 'https://chatters.ca', None, 'https://www.fountainssouthend.com/?utm_source=Yelp&utm_medium=Local&utm_campaign=Organic&utm_content=HomePage', None, 'http://www.allpeopleschurch.ca', None, 'http://www.sundevilauto.com/locations/az/phoenix/ahwatukee-16', 'http://www.freshandeasy.com/', 'http://www.hawthornemgmt.com', 'http://hurtsdonutco.com', None, 'http://www.michaelcoxen.com', 'http://www.ampmairconditioninginc.com', None, 'http://www.pizzahut.com/', 'https://www.tramontodentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', '1592678080', None, None, 'http://www.jimmythegreekgroup.ca', None, 'https://www.wellsfargo.com', None, 'http://www.eccgolf.com', None, 'http://www.papadavinci.com/', 'https://www.homedepot.com/l/East-Liberty/PA/Pittsburgh/15206/4136?cm_mmc=seo-yelp&', None, None, 'https://www.chaplocklocksmithnortholmsted.com', 'http://www.rickhobbs.net?cmpid=CU6M_BLM_0006', 'http://tenrenteatime.ca/', 'https://www.marysbsweets.com', 'http://www.neptunesociety.com/location/phoenix-cremation', 'http://www.caremore.com', 'http://habanerosmg.com/habaneros/home.html', 'http://666Manning.pourboy.ca', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.luchita.com/', 'http://www.vincemarinoplumbingllc.com', None, 'http://usps.com', 'https://www.4thstreetpizza.com', None, 'http://www.roctitle.com', None, 'https://www.eyeglassworld.com/store-list/las-vegas-(s)-nv-89121/', 'http://www.x929.ca', 'https://www.mandalaybay.com/en/casino/race-sports-book.html', 'http://www.detailkings-lv.com', None, None, 'http://www.moogaudio.com/', 'https://www.fastmed.com/urgent-care-centers/charlotte-nc-walk-in-clinic-west-mallard-creek-church-road/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', None, 'http://www.agilitymovingandstorage.ca', '1592678194', 'http://www.cafetoscanoinaurora.com/', None, 'https://amaidforaday.ca', 'http://www.theguitarworldoakville.com', None, 'http://www.chillitAZ.com', None, 'https://www.usps.com/', 'https://www.a-aaakey.com/locations/key-storage-arizona-252/?utm_source=yelp&utm_medium=paid', None, None, 'https://www.chapmanvalue.com/search/used/scottsdale/cars', 'https://www.kohls.com/stores/az/phoenix-613.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.tuesdaymorning.com', 'http://www.agelessmimedspa.com/', None, None, 'https://locations.panerabread.com/oh/amherst/46402-middle-ridge-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://federicosmexicanfood.com', None, None, 'https://milios.com', 'http://www.rossstores.com', None, 'http://www.saloneclipse.com', 'http://www.bbhc.net', 'https://empiregaragedoorlv.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.03116.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03116', 'http://www.zebramedicine.net/default.html', 'https://www.bostondentalgroup.com/locations/affordable-dental-durango/', 'http://www.hatlenfamilychiropractic.com', 'http://forzastone.com', 'http://nailshine.ca', 'http://www.macayo.com/location/scottsdale/', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2fpa%2fpittsburgh%2fairport&sisearchengine=1524&siproduct=2707_Bus', 'https://www.frysfood.com/stores/details/660/00074?cid=loc66000074_gmb', 'http://www.mybobs.com?utm_medium=local&utm_source=yext&utm_campaign=yextlistings&utm_term=pennsylvania&utm_content=126%20monroeville%20pa', 'http://www.lochandquayto.com', None, 'http://www.jerrycoy.com', None, None, 'http://www.thefranciscanapts.com', None, 'http://www.caferio.com/', None, 'https://torontopearson.com/Components/Templates/Retailer.aspx?RetailerID=21474839220', 'https://www.gpscentral.ca', 'https://dropsauna.com', 'http://www.aircanada.com', 'https://www.houdini.com/venetian', None, 'https://locations.jackinthebox.com/us/az/youngtown/11101-nw-grand-ave', 'https://www.thevenueapartments.com', 'http://8020hub.ca', None, None, 'http://www.curryaway.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPITCA', 'http://www.cosmoscollision.com', None, 'https://agents.allstate.com/brittny-perry-las-vegas-nv.html', None, 'http://www.rossstores.com', None, 'https://www.galvanize.com/phoenix/campus', 'https://locations.theupsstore.com/az/scottsdale/16211-n-scottsdale-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'http://motherbunchbrew.com/', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.granadapestcontrol.com', 'http://www.stircrazy.com', 'http://www.starbucks.com/store/15818/', 'http://www.brickandbarrelbrewing.com', 'http://www.rockychoc.com/location/mississauga-square-one-shopping-centre/', None, 'http://www.centralgrille.net', 'http://www.alofttempe.com', 'http://www.forwardlanes.com', None, None, 'https://www.ttc.ca/Subway/Stations/Dundas_West/station.jsp#Schedule_', 'http://stores.partycity.com/oh/cleveland', 'https://azhealthinsurancebrokers.com', 'http://adidas.ca', None, 'http://dignityhealth.org/doctor/WF_FindADoc_Profile.aspx?id=bebc0c9f-060a-48a7-960c-49de56343416', 'https://www.simonmed.com/locations/all/simonmed_imaging___dobson_village_i', None, None, None, None, 'https://us.megabus.com/?utm_source=Yelp&utm_medium=Yelp&utm_campaign=LasVegas%20Page', None, 'http://www.babyview.ca', None, 'http://www.deserteaglecoffee.com', 'https://primpandblow.com/locations/hayden-peak-crossing-north-scottsdale/?UTM=yelp', 'https://www.cheetahsaz.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'https://www.mmfoodmarket.com/en/store-locator', 'http://www.shenisautotrend.com', None, 'https://locations.sonicdrivein.com/nv/lasvegas/6301-w.-lake-mead-blvd..html', 'http://www.shenanigansgrille.com', 'http://www.firstmutualrealty.com', 'http://www.drdavidglassman.com', None, None, None, None, 'http://www.6651customs.com/', 'http://www.montevidarentals.info', 'https://stacktmarket.com', 'http://atlasimprov.com', 'https://elitebabyservices.com', '1592678468', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/downsview-6000-dufferin-street.aspx?postalcode=M3H+5T5&storeid=21', 'https://locations.noodles.com/wi/madison/3600-university-ave-and-midvale-blvd.html', 'http://www.muserestaurant.ca', 'https://locations.sonicdrivein.com/az/avondale/601-north-central.html', None, 'http://www.zaytoonkabob.com', 'https://myredmountainfamilydental.com', 'http://www.foothillsrehab.com/', 'https://www.azvetdentists.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.lakelasvegasgelato.com', 'http://www.actionrentsrantoul.com', 'http://Autobahnlv.com', 'https://www.atmosphere.ca/stores/calgary.html', 'http://www.scoopspittsburgh.com/', '1592678510', 'http://www.beddrs.com', 'http://makerpizza.com', 'http://afterhoursrestoration.com', 'http://www.greatclips.com/', 'http://www.phoenixtattooremoval.com', None, None, 'http://www.lasvegasrealestateneeds.com', 'http://herbalnailspa.com', 'http://www.madisongroveapartments.com', 'http://www.thatitalianplace.ca', '1592678540', 'https://www.homegoods.com/store-details/Las-Vegas-NV-89149/312', None, 'http://primoprimecharlotte.com', None, None, 'http://www.2cats.ca/', '1592678557', 'http://bellavistaim.com/', 'http://stjosephanimalhospital.net', 'http://southplaza.dentalworks.com', 'https://www.currys.com/generic.htm?ECINFO=oakvillestore', 'https://www.extraspace.com/storage/facilities/us/arizona/tempe/501572/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, 'http://www.uber.com', 'http://www.cgspizzalv.com/', 'http://superlubecarcare.com/avonsl.html', 'http://www.bloomsalonandspalv.com', 'http://www.jackmussey.com?cmpid=B1HW_BLM_0006', 'http://mayapmu.com', None, 'http://labellabridalaz.com/', None, None, None, None, 'https://www.linkedin.com/in/susan-daubenbis-12aa2b15', 'https://www.wyndhamhotels.com/hotel/28023?tel=18885951878&iata=00093785&cid=fe:mt:20170424:yl:pp:MTUS:28023', 'http://www.force-sports.com/Default.aspx?tabid=208812', 'http://www.nachotattoousa.com', 'http://strebelectric.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, None, 'http://www.desigrill.ca', None, None, 'https://www.macu.com/Branch-Locations/AZ/Goodyear/Goodyear-Branch/0150', None, 'http://www.childrensheartcenter.com/', 'http://www.barkbusters.com', 'http://www.craiggillespie.com', 'http://www.arizonayarn.com', 'http://www.urbansouthwest.com/', 'http://www.westwinddriveins.com/view_theater_scottsdale.php?id=3998', 'https://www.chinachina.ca', 'http://www.swissdreambeds.com', 'http://www.rainbowshops.com', None, 'https://www.dignitymemorial.com/funeral-homes/sun-city-az/sunland-memorial-park-mortuary-cremation-center/4279', None, 'http://www.aandadentistry.com', None, 'http://www.silverstatecleaningservices.com/', 'http://vaffi.ca', 'http://www.huntamps.com', 'http://rollinsmokebarbeque.com/', None, 'https://www.thejoint.com/arizona/phoenix/arcadia-48011', None, 'http://www.grayhawkeye.com', 'http://hoteltheodore.com/cielorestaurant.asp', None, 'http://www.mysfarizona.com/?cmpid=w36f_blm_0006', 'https://www.aftercare.org', None, 'http://www.thatbbqjoint.com/', 'http://www.fitbodybootcamp.com/strongsvillefitnessbootcamp/', 'http://www.wetzels.com', None, 'http://www.SuperTouchRvDetail.com', '1592678694', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=14217&localechange=1', 'http://www.harveys.ca/', 'https://www.mattressfirm.com/stores/az/peoria/mattress-stores-peoria-az-85382-8181.html', 'http://www.bannerhealth.com/locations/phoenix/banner-physical-therapy-mcdowell?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://www.ookahibachi.com', 'http://www.thearcherygame.com', 'http://montgomerymazda.com/', None, 'https://thaiexpress.ca', 'http://www.gnc.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.spigoloristorante.ca', 'https://eliteplasticsurgeryaz.com', 'http://wholesalewindowanddoor.com', '1592678734', 'http://www.carproaz.com', None, None, 'http://www.vanityglocharlotte.com/', 'http://buckandrider.com', 'http://www.JimmyJohns.com', 'http://laothairestaurant.net', 'http://www.pandoralv.com', 'http://www.tintofexcellence.com', None, 'http://www.2houndsdesign.com', None, 'http://www.dunkindonuts.com', 'https://locations.dennys.com/OH/MENTOR/247936', 'http://www.thepearlspa.ca', 'http://www.bk.com', None, 'http://www.juniperluxury.com', 'http://www.spiritpgh.com', None, None, 'https://www.spoonerpt.com/locations/mesa-gateway/', 'http://www.citrusmedical.ca', 'https://irmaskitchen.business.site', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.lexingtonlaw.com/?tid=32161', 'http://www.byollia.com/', 'http://www.charlottenc.mistersparky.com', None, 'https://www.target.com/sl/sun-prairie/2491', 'http://www.phoenixazchiropractors.com', 'http://www.hairsalonmesa.com/', 'http://www.northwesttoyota.ca', 'http://www.metropolitanwindows.com', '1592678814', None, 'http://www.vanhouteninc.com', None, 'http://wychwoodparkanimal.com/', '1592678827', 'http://www.toronto-chinatown.ca', 'https://www.drramoslasvegas.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://goodwillscwi.org', 'http://www.bistro185.com', 'http://www.jcastrolawgroup.com', None, 'http://www.pietrosingomar.com', 'http://www.calanbeefnoodle.ca', None, 'http://www.yifangtea.com.tw/en/index.php', None, None, 'http://www.room2bein.com', None, None, 'https://redsrestaurants.com/locations/reds-square-one/', '1592678876', 'http://www.starbucks.com/store/9298/', 'http://skincarephoenix.com', None, 'http://www.carefreechurch.com', None, None, None, 'http://www.whichwich.com/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.applebees.com/en/restaurants-garfield-heights-oh/9225-vista-way-75098', None, None, None, 'http://www.sunrisefootandankle.com', 'http://www.santanfamilymedicine.com/', 'http://www.chefsatyourhome.com', 'https://www.littlesmilesofsurprise.net', 'http://augustmoon.ca', None, 'http://jtnailslasvegas.com', 'http://www.sincitychocolatefestival.com', None, 'http://absolutehealthaz.com/', 'http://www.mastermechanic.ca/locations/home.php?location=Oakville', None, 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', 'https://www.crossfithuntersville.com', None, 'http://www.botanistofthevalley.com', None, None, None, 'http://www.michelefanelli.com?cmpid=GH0M_BLM_0006', 'https://www.thecleaningauthority.com/madison/', '1592678994', None, None, None, 'http://www.westsidediscountmuffler.com', 'http://www.specialtycarburetors.com/', 'https://local.fedex.com/az/avondale/office-1427/', 'http://www.lvterrace.com', None, None, None, 'http://www.kfc.com/storelocator/Default.aspx?address=2023%20E%20Lake%20Mead%20Blvd,North%20Las%20Vegas,NV', 'http://www.senorbluesmobile.com/', None, 'http://www.mariecallenders.com/', None, 'http://www.agapepodiatry.com', 'http://californiaclassics.ca', 'http://www.buffersalon.com', 'http://www.charlieslasvegas.com', 'http://www.drimplantsurgery.com', 'http://www.couturebridelasvegas.com', 'http://www.wonderfulworldofcircus.com', 'http://soupersalad.com/', None, 'http://www.nuancefacialplastics.com', None, None, '1592679080', None, 'http://www.mitazafusionpizzeria.com', 'http://www.wingmachine.com', 'http://puls.com/tv-mounting', '1592679100', 'https://www.phoenix.gov/parks/parks/alphabetical/e-parks/encanto-park', None, 'http://ultranails.com/', 'http://www.tacobell.com/', 'http://www.cillierscpa.com/', 'http://www.akleenerimage.com', 'http://www.amandajoyclean.com', 'https://www.cccnevada.com/treatment-centers/lung-center-of-nevada/', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=101357', 'https://www.chick-fil-a.com/henderson', 'http://mapleleafs.nhl.com/', None, 'http://www.capCORErealestate.com', 'http://tritonautospa.com', 'http://symposiumcafe.com/ajaxrestaurants.html', None, 'http://www.mountaingear.com/rrr', None, '1592679163', 'http://www.villapizza.com', 'http://waldhorn.us', None, 'http://www.coldstonecreamery.com/stores/20001', 'http://unionhillsanimalhospital.com', 'http://www.la-z-boy.com/Northeast-Ohio/Brookpark-Road', 'https://waalflower.ca', 'http://www.bartelspethospital.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=jan16', 'http://www.norascuisine.com/', 'http://www.bunnacoffee.com/', None, None, None, 'https://www.capellibabe.com', None, 'http://www.nevadaheart.com', 'http://www.juddsf.com?cmpid=k2wa_blm_0006', 'http://www.beckwithorchards.com', None, 'http://www.bourbonstreetbarrelroom.com/', None, 'https://www.dillards.com/stores/beachwood-place-beachwood-ohio/0365', None, None, None, 'http://boombozztaphouse.com/', 'http://www.bonterrabuilders.com', 'http://onejet.com', 'http://www.wingstop.com', 'http://belmonteraw.com/', None, None, None, 'http://www.zekescoffeepgh.com/coffee-drive-thru', 'https://www.petsmart.com/stores/us/pa/pittsburgh-store0586.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://locations.sonicdrivein.com/az/surprise/13924-n-litchfield-road.html', 'https://www.spectrum.com/locations/oh/north-olmsted/24910-lorain-rd', 'http://www.studiobronzelasvegas.com', 'http://gandbfencelasvegas.com', 'http://www.unionhillsapartments.com', None, '1592679300', None, None, 'https://mariachis-mexican-food.business.site/?m=true', 'http://torontohockeyrepair.com/', 'http://www.sincityoffroad.org', 'https://victusintegrative.com', 'https://nationwidevision.com/locations', 'http://www.jonnybegooddogtraining.com', 'https://www.victorslandscaping.net', 'http://berriesandbloomscatering.com/', 'http://truckcandy.com', '1592679347', None, 'http://www.fashioncrimes.ca', None, '1592679362', None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7784&localechange=1', 'http://freshexclusive.com', 'http://glacierwater.com/about-glacier/', 'https://locations.crackerbarrel.com/oh/copley/114/', 'http://www.aquafilterfresh.com', 'http://www.phoenixpubliclibrary.org/Locations/Pages/Acacia.aspx', None, None, 'http://tesla.com', None, None, None, 'http://www.shilandfamilymedicine.com', 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://crazyhorse.com/Bedford-Hts-Ohio/', None, 'https://www.moneytreeinc.com/branch/north-nellis', 'https://www.hydrosolution.com/', None, 'http://www.thefutonstore.net', 'http://iphixation.com', 'http://www.bk.com', '1592679438', 'http://www.phoenixazaccountingtax.com', 'http://todaysdentistryspa.com', 'http://www.phxbeerco.com', 'http://www.divawomenswear.com', 'http://www.lazeezshawarma.com', 'http://www.aspenpoolsaz.com', 'http://www.vegasluxury.com', 'http://platinumrentalexperience.com', 'http://www.4getmad.com', 'https://www.autobell.com/locations-hours/south-carolina/charlotte-area/964-cabela-s-drive.html', 'http://www.sjp-collection.com', None, 'https://paramountfurnitureltd.ca', 'http://www.roxianlive.com', '1592679488', None, 'http://www.ocotillogolf.com', 'https://sunsetstation.sclv.com/Gaming/Sports-Book?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.markyfresh.com', '1592679506', 'http://www.foxcroftwine.com', 'https://www.simon.com/mall/the-shops-at-crystals', None, 'https://www.biolifeplasma.com/us/#/donation-center?centerId=148', 'http://altovineyards.net/', 'http://www.goodglendalehomesforsale.com', 'http://www.bk.com', None, 'https://www.gerbercollision.com/locations/las-vegas-decatur-blvd-nv', 'http://thedynastycuisine.com', 'http://www.stonecreekgolfclub.com', None, 'http://www.1stopautomall.com', 'http://www.allfamilycarepc.com', None, None, '1592679564', None, 'https://locations.theupsstore.com/nc/charlotte/2820-selwyn-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.lasvegasnvlocksmiths.com/', 'http://www.ledrewcostello.com', None, None, 'http://www.paideiaacademies.com', 'http://www.704granitemarble.com', 'http://universalwaterservice.com/', 'http://www.driveclassicmini.com', '1592679600', 'http://drystaraz.com', 'https://stores.madewell.com/en/hilldale-shopping-center?srccode=X%7CPMG%7CNaturalSearch%7CLocal%7CYelp%7C235', 'http://www.reneesflowers.net/?srccode=yelp_track', 'https://www.brakesplus.com', None, 'http://www.BenandKellyPhotography.com', 'http://www.pizzapizza.ca', 'http://www.picklebarrel.ca/restaurant/location/newmarket/', 'https://www.petsuppliesplus.com/Store/PA/Robinson-Township/Robinson-Township/202?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'http://shopnsavefood.com', 'http://www.starbucks.com', None, None, None, 'http://www.sparklincleancarwash.com', 'http://www.fruitland.us', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.southhillsplumbing.com', 'http://www.rebeloil.com/', None, 'http://www.themadisongrille.com', 'http://www.AllBridesBeautiful.com', 'http://www.ramentimeaz.com', 'http://www.thedogbowl.ca', None, 'http://www.fihnintegrativecare.com', 'http://charmeck.org/mecklenburg/county/ParkandRec/Greenways/OpenGreenways/Pages/LowerMcAlpineCreekMcMullenCreekandFourMileCreekGreenways.aspx', None, None, 'http://www.polotowers.com/?mkc=ptsyelpdr&utm_content=Book+direct+and+save+additional+10%25+&utm_medium=Booking+Button&utm_source=Yelp&utm_campaign=Yelp+Direct+Booking+-+MKC+PTSYELPDR', 'http://arizonadentshop.com/', None, '1592679720', None, 'http://www.xtazapgh.com/', None, 'http://www.myodetoxperformance.com', 'http://www.allamericanoutdoorliving.com', 'http://www.gigglypanda.com', 'https://www.thearizonamedicalclinic.com', 'http://seattle-espresso.com', 'http://www.ajheilflorist.com/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.unitedmoversandstoragellc.com', 'http://www.midas.com/lasvegas/store.aspx?shopnum=1192&dmanum=480', 'http://www.mayatux.com', 'http://www.ambiancebeautybar.com', 'http://www.chronicpa.com', 'http://cybercitycomix.com/', 'http://www.mastermechanic.ca/TorontoHighPark/', 'http://www.cltpediatricdentistry.com', 'http://www.wliaz.com/location/gilbert/', None, 'http://www.shopthreadonline.com', 'http://www.blueberryhillrestaurants.com/', None, 'http://www.loosemoose.com', 'http://www.jspestcontrol.com', 'http://www.dunkindonuts.com', 'http://gloriousflowershop.com', None, 'http://www.peterpiperpizza.com/', 'http://www.formaplasticsurgery.com/', 'http://www.matageframing.com/', 'http://www.pritchettephysicaltherapy.com', None, None, 'http://childrensedationdentist.com', 'https://www.cosmopolitanlasvegas.com/lounges-bars/the-chandelier?utm_source=yelp&utm_medium=organic&utm_campaign=yelp', 'http://laced-lv.com', 'http://www.heritagepostersandmusic.com', None, None, 'http://www.suryacalgary.com/', None, 'http://www.kimberlyjewelry.com', 'http://www.fitbodymadison.com', None, 'http://www.SyntheticTurfSystems.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.marriott.com/hotels/travel/cltrd-residence-inn-charlotte-city-center/', 'http://www.PrincipleMoving.com', None, 'http://powerranchstorage.com', 'https://tiborskoshermeats.com', 'http://www.perfectshotphotobooth.com/phoenix-photo-booth-rentals/', 'http://www.superstore.ca', 'http://www.popeyeschicken.ca', None, 'http://frysfood.com', 'http://www.petsonpointllc.com', 'http://negrilsjerkhut.weebly.com', '1592679928', 'http://www.fitworks.com/willoughby', 'http://www.kegsteakhouse.com/en/locations/AB/calgary/stadium-keg/', None, None, 'http://www.gcflight.com/', 'https://eastside-landscaping.com', 'http://crepesagogo18yorkville.com', 'https://www.garagedoorservice.com/phoenix', 'http://www.homeoutfitters.com', None, 'http://www.ihg.com/crowneplaza/hotels/us/en/independence/clerr/hoteldetail', 'https://www.greenfieldfamilydentist.com', 'http://www.sunnymummy.com/', 'https://www.seniorlifestyle.com/property/arizona/thunderbird-senior-living/?utm_source=yelp&utm_medium=Business%20URL', 'https://european.ca', 'https://www.mgmresorts.com/en/hotels/united-states/mgm-northfield-park.html', 'https://www.expressoil.com/stores/tempe/az/3500/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.mgmgrand.com/en/restaurants/mgm-grand-buffet.html', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://fitnesstogetherhuntersville.com', 'http://www.therosebarandgrille.com', 'http://www.quiktrip.com', 'http://www.fountaintire.com/stores/airdrie', None, 'https://www.carmax.com/stores/7244?adcode=YLP7244&utm_campaign=LG_AFF&utm_source=LG_AFF_YLP&utm_medium=local&utm_content=shop', 'https://corbosbakery.net', 'http://www.eatmrmesquite.com', None, 'http://www.residential-leasing.com', 'http://pinnaclesports.org/', 'http://www.bestofchinesemedicine.com', None, None, 'http://www.englishbayfish.ca/', 'http://hobbybenchstores.com/contact', 'http://eighteeneight.com/fitchburg-wi?utm_content=weburl&utm_medium=organic&utm_source=yelp', '1592680052', 'http://www.concordcustomcleaners.com', None, 'https://www.ethanallen.com/on/demandware.store/Sites-ethanallen-us-Site/en_US/Stores-Details?StoreID=193&utm_source=yelp&utm_medium=organic&utm_campaign=unpaid_listing&utm_term=193', 'http://www.beautyspatoronto.com', 'http://journeyautosales.net', None, 'http://www.reyesdental.com', 'http://www.mulliganslasvegas.com/', '1592680078', 'http://www.chandleraz.gov/Content/Paseo_Trail_Map.pdf', None, 'https://www.ascari.ca/kingwest', 'http://www.911supply.ca', '1592680096', 'http://www.regencytransportation.com', 'http://www.vuaurology.com', 'http://thegoodgoatgallery.com/', 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?language=en&STORE=5', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280197177&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.sunsetcoveliving.com', 'https://locator.chase.com/az/tempe/4714-s-rural-rd?jp_cmp=rb/LocalListings/aff/branch/na', None, '1592680126', 'https://www.ulta.com/stores/mesa-az-57', 'http://www.coneyislandfriedchicken.com', 'http://www.danslasvegas.com', 'https://www.allans-flowers.com', 'http://discountrvrepair.com', None, None, None, 'http://hcws.org', 'http://www.amayarestaurant.com/', 'http://www.tremontplacelofts.com', None, 'https://mesaazelectricians.com', 'http://www.albertafirearms.com/', 'https://www.petsmart.com/stores/us/az/phoenix-store0131.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://locations.massageenvy.com/arizona/glendale/5143-w.-olive-ave..html', None, 'http://www.dunkindonuts.com', None, 'http://cavacinigardencenter.com', 'http://www.straightlinesuspension.com/', 'http://www.thefindyourself.com/almostthere', 'http://www.banfield.com?utm_source=yelp&utm_medium=PAID&utm_content=yelp_general&utm_campaign=YelpPaid', 'https://starfirewebdesign.com/website-designer-las-vegas/', 'https://www.ediblearrangements.com/stores/930-W-Broadway-Tempe-AZ-85282', 'http://www.villapizza.com', None, 'http://www.UnitedBeautySupply.com', None, 'http://www.shoemill.net', 'https://elementsmassage.com/yelp-herbal-ritual-special?loc=Scottsdale_North', 'http://www.goelemental.ca', 'http://www.tuesdaymorning.com', 'http://www.mahasfalafil.com', 'https://vmcfortmill.com', 'https://mytownsquarelasvegas.com', 'https://www.hiddencoveapthomes.com', 'http://www.metrolexus.com', None, 'http://www.vibetality.com', '1592680259', None, 'http://www.sallybeauty.com', None, 'https://www.ilrionepizzeria.com', 'http://inglotusa.com/store-locator-search-results?cid=11', None, None, None, None, 'http://mtpleasantvet.ca', None, 'https://www.smilesdivinetmd.com', 'http://www.autotags1.com', '1592680309', 'http://diamondimagecutz.com', 'https://steakfritesoki.ca', 'http://mcldaz.org/litchfieldpark', 'https://www.simonmed.com/locations/all/simonmed_imaging___sun_city_west', 'http://carpetcleanlv.com', 'https://satruck.org', None, None, None, None, '1592680343', 'http://www.valleymedicalweightloss.com', None, None, 'https://bhmanagement.com/communities/nc/charlotte/elements-on-park-apartments-1350', None, 'http://www.askdrkan.com', 'http://www.venericameats.com', 'http://taxanista.com', None, None, None, None, 'http://www.controlthebugs.com', 'http://www.c5-tnr.org', 'https://www.theskinshopscottsdale.com', None, 'https://www.brainbalancecenters.com/locations/mesa/', 'http://www.trendvape.com', None, 'http://www.koa.com/campgrounds/streetsboro/', 'https://www.fastmed.com/urgent-care-centers/tempe-az-walk-in-clinic-asu/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.paramountfinefoods.com', 'http://www.expressflooring.com/?utm_source=VYRL&utm_medium=Yelp&utm_campaign=Glendale', 'http://bananarepublic.gap.com/', None, 'http://www.celebritytanning.com', None, 'http://www.roselandlanes.com', 'https://www.thekingsjewelry.com', None, None, 'http://www.centennialhyundailasvegas.com', None, 'http://www.elysianatthedistrict.com', 'http://www.coffeebean.com', 'http://www.copenhagenliving.com', None, '1592680472', 'http://www.houseofcarschinook.com', None, None, 'http://wildpeacockantiques.net', 'http://www.slidinthru.com/hq', 'http://www.thecreativestack.com', None, 'http://www.bsidebeauty.ca', None, 'http://www.camelbackmazda.com', None, None, 'http://www.comedycave.com', 'https://www.walgreens.com/locator/walgreens-5975+weddington+rd-matthews-nc-28104/id=10255', 'https://www.statefarm.com/agent/US/NV/Las-Vegas/Brooks-Whitmore-GG9RC5FYBAK', 'http://www.mesabattingcages.com', None, 'http://azhitchmanandautotint.com/', 'http://www.goldenspoonlasvegas.com', 'http://chase.com', 'http://www.prestigechryslerjeepdodge.com/', None, 'http://www.lifttechgarages.com', 'https://sweet-marys-ice-cream-yogurt-sorbet.business.site', 'http://www.safarigolfaz.com', 'https://www.azmediquip.com', '1592680555', 'http://www.affordablecharlotteshuttle.com', 'http://www.sallybeauty.com', None, None, None, 'http://www.elricos.com', 'http://www.reptilerapture.net', 'http://club935.net/', None, None, 'http://www.silviasfloraldesign.com', '1592680590', None, 'https://swedishsolution.com', '1592680600', 'http://www.thedarkroombar.com', 'http://www.paperland.ca', 'http://planetbeach-expressaz.com', 'http://lululemon.com/toronto/queenstreet?cid=yelp', '1592680620', None, '1592680625', 'http://pestcontrollasvegasvalley.com', 'http://www.adrianspizzaand6packs.com', 'http://www.normscar.com/', None, 'http://www.noblesrestaurants.com', None, 'https://www.clearchoice.com/locations/dental-implants-cleveland/?trans_id=webdisyelp&utm_campaign=Yelp&utm_source=YelpListing&utm_medium=Listing', 'http://www.hairclassicssalon.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', '1592680656', 'http://michelesullivanluxuryhomes.com', None, 'http://www.calpool.com/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.villapasta.ca', '1592680681', 'http://my.clevelandclinic.org/locations_directions/Regional-Locations/solon-fhc', None, None, 'http://reedand.company', 'http://www.udallshumway.com/', 'http://clk.atdmt.com/MGM/go/384964017/direct/01/', 'http://www.levireatelier.com', 'https://www.enterprise.com/en/car-rental/locations/us/pa/bridgeville-4033.html?mcid=iyp:8368400', None, None, None, 'https://www.chick-fil-a.com/arboretum', None, 'http://www.tomswarehousesale.com', None, 'http://www.essenceandherbs.com/', 'https://meridiemaz.net', 'http://www.mgmgrand.com', 'http://tacosnritas.com', 'http://crossfitsanctify.com/', None, None, None, 'https://digipathlabs.com', 'https://www.zara.com/ca/', 'http://www.unimarket.ca', 'http://wikbsolutions.com', 'http://iconzbar.com', None, 'http://www.vacanthousecleaners.com', 'http://www.roguetattoo412.com/', None, 'https://www.goanddrive.com', None, None, 'https://www.kidsquest.com/location/boulder/', 'https://www.nofrills.ca/store-locator/Jim%27s+nofrills/3937?storeId=3937', None, 'http://www.evenstevens.com', 'http://bocalocaburritofactory.com', None, None, 'http://footsolutions.com/goodyear-arizona/', 'http://www.dfkonline.com/monroeville', '1592680819', None, None, None, None, 'http://www.northscottsdalewomenscare.com', None, None, 'http://www.picturepeople.com/default.aspx?PK=e3adeef4-54b4-43c6-990a-619531e6637b', 'https://www.thirdfederal.com?=ad.doubleclick.net/ddm/clk/458420725;262568795;w', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.tmcandmore.com', None, None, 'http://www.qualitydriving.ca', 'http://www.charlottecustomcouture.com', 'http://www.venetian.com/Las-Vegas-Entertainment/Resident-Shows/Soul2Soul/', 'http://thaiculture.ca', 'http://www.dunkindonuts.com', 'http://www.behandpicked.com', 'http://www.usnwc.org', None, 'http://www.fitnessworks.com/', 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', 'http://www.classicbowl.com', 'http://www.bajafresh.com/stores/30407', 'http://www.dfckidsdentist.com/markham-office-location', 'http://www.cafemoka.ca/', 'http://www.hickoryhillskennels.com', '1592680916', 'https://www.undergroundfitnessaz.com/locations.html', None, 'http://www.rumbleboxing.com', None, '1592680933', None, None, 'https://actux.com/storelocator/parma-oh-6/', 'https://www.batteriesplus.com/store-locator/il/peoria/batteries-plus-278?utm_source=yelp&utm_medium=local&storecode=278', 'https://www.simplygreenpest.com', 'http://kimberlyannstearoom.webs.com/', None, 'http://soundandlighthealing.com/index.html', 'http://www.timhortons.com/ca/en', 'https://chatters.ca', 'http://www.totalpatioaccessories.com', 'http://www.socialhouse7.com', 'https://www.appliancerepairteam.ca', 'https://www.medicalwastedisposal.com/locations/arizona/', 'https://www.marriott.com/golf-hotels/phxcb-jw-marriott-scottsdale-camelback-inn-resort-and-spa/camelback-golf-club/5256759/home-page.mi', 'https://4cbroastchickenalbaikstyle.com', None, 'http://blackmagicwednesdays.com', None, 'http://blenz.com/', 'http://clicks.dbm-media.com/Yelp_mobile', 'https://locations.waxcenter.com/pa/mccandless/mccandless-0287.html', '1592681010', 'http://popeyes.com', 'http://www.wagontrailrv.com', 'https://locations.massageenvy.com/north-carolina/gastonia/2290-e-franklin-blvd.html', None, None, None, '1592681028', 'http://www.afcMed.com', None, 'http://www.bobstranny.com', 'http://sassyscafeandbakery.com', 'http://www.streetcafeaz.com/', None, 'https://www.mattressfirm.com/stores/az/goodyear/mattress-stores-goodyear-az-85395-6648.html', 'http://summerlink.com/parks', 'http://www.balboapizzalv.com', 'http://loschicosbrasa.com', 'http://www.holidaycarrentals.ca/', 'http://www.studio21tattoo.com', 'http://tiedphotography.com/', None, 'http://www.calligramme.us', 'http://fishbar.ca/', 'http://www.gadgetexpertslasvegas.com/', None, 'http://www.nikkithemua.com', 'http://srwc.unlv.edu/theSHC.html', None, 'https://www.dialcarpet.com', 'https://www.steaknshake.com', 'http://citywidegaragedoor.com', 'http://www.babykayscajunkitchen.com', 'http://www.jumpingriceandrolls.com', None, None, 'http://www.TMofPGH.com', 'https://www.intermixonline.com/storeresults?dwfrm_storelocator_maxdistance=30&dwfrm_storelocator_countryZip=US&dwfrm_storelocator_postalCode=85254&dwfrm_storelocator_findbyzip=Search&dwfrm_storelocator_distanceUnit=mi', 'http://savarinobrothers.com', 'http://www.usls.biz', None, 'http://www.provasalon.com', 'https://www.iqfoodco.com', 'http://www.copperkettleaz.com', None, 'http://theeggsperience.ca', 'http://jetsunsjuicyburger.com', 'http://earlscollisioncenter.com', 'https://myoptometristcalgary.ca/health-first-optometry/', None, 'http://Guacboxaz.com', 'https://elginmills.orangetheoryfitness.com?utm_campaign=yelp&utm_term=072017&utm_medium=print&utm_source=redirect&utm_content=yelp_print', 'http://www.easternindoorswapmeet.com/', None, 'https://local.lenscrafters.ca/on/mississauga/100-city-centre-dr.html', 'http://www.pinecreststrose.org', 'http://www.mesasignshop.com', None, None, 'http://www.harryrosen.com/store/Bloor%20Street', 'http://www.charleyssteakery.com/', 'http://www.grayhousepies.com', None, 'https://www.popeyes.com/store-locator/store/restaurant_84073', 'http://www.pleasureparadisespa.com/', 'http://www.scarboroughribfest.com/', None, 'http://www.upstagenoda.com', None, 'http://www.traxfarms.com/', 'https://www.budgetflooringlv.com/yelp-offer', 'http://www.prideoferin.pub', None, 'http://www.vvsjewellers.com', None, None, 'http://calabashrestaurants.ca', 'http://whizkidzpreschool.com', 'http://www.lasvegasautosports.com', 'http://www.johncaparulo.com', 'https://gotmemories.com', 'http://www.chinastar-pgh.com/', None, 'http://www.damagecontrol-us.com', None, 'http://www.opticalthirty8.com', 'http://www.thesweetlifeconcord.com', '1592681322', 'http://www.terribleherbst.com', 'http://www.arizonaluxurylawns.com', None, '1592681336', 'http://www.brilloboxpgh.com', 'http://www.no-regrets-tattoos.com', 'http://www.vegasdiscountnutrition.net', 'http://victoryma.com/school/mesa-az', 'https://www.famousfootwear.com/?partnerid=YELP', 'http://www.Inspectionlv.com', 'http://www.nygh.on.ca', 'http://www.KiranAndKiran.com', None, 'http://www.vegaschaletmotel.com', 'http://www.winnerscirclecollision.com', 'http://www.nbtaekwondo.com', None, None, 'http://www.wildhorsewest.com/', 'http://www.thesterlingpark.com', None, None, 'http://www.creativesmilesaz.com', 'https://www.thehairapist702.com', None, None, 'https://www.fairwayindependentmc.com/locations/arizona/scottsdale-4727', 'http://www.inetworkautogroup.com', None, 'http://allaboutpawsvegas.com', 'http://www.mapledragon.ca', 'https://locations.wendys.com/united-states/oh/north-ridgeville/34323-center-ridge', None, 'http://www.healthyplanetcanada.com', 'http://www.lecupcakeshoppepgh.com/', 'http://www.jessinailstoronto.com', None, 'https://hudsonauctionaz.com', 'http://trespesosnc.com/', 'https://fetchingdog.net', None, 'http://olivemyheart.com', 'http://www.thecakecontessa.com', 'http://www.annesportun.com/', 'http://bread-stuff.ca/', None, None, None, None, 'http://www.gordonshoes.com', 'http://charleyscaribbeancuisine.com', 'https://www.brakesplus.com', 'https://www.abckidseyes.com', None, 'http://www.atmacenter.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZXR', 'http://www.shopstaticmotorsports.com', 'https://www.aiotheeyesurgeonswestmifflin.com', None, 'http://montrealdeliandgreekgrill.com', 'https://stores.arhaus.com/az/scottsdale/7030-e-greenway-parkway.html', 'http://www.larchmererugs.com/', 'http://www.juniorspizzeria.com/', None, 'http://www.wildemeyer.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.luckylins.com', None, None, None, 'http://www.dollarama.com', 'http://www.urbanatruetires.com', 'http://www.mikesautoservice.ca', '1592686819', 'https://www.be-em.com', 'http://www.secondcup.com/location/toronto-355-danforth-avenue', None, 'https://movement.com', 'http://www.theglamparlor.com', 'http://www.blueskyjava.com', 'http://www.stclairdental.ca', 'https://www.wellsfargo.com', 'http://www.az-pro-realty.com', 'http://oakvillehonda.ca', 'http://www.phoenixmoonacupuncture.com', None, 'http://www.teavana.com', 'http://www.arthousegilbert.com', None, None, None, 'https://www.acupunctureliving.com', 'http://www.paversealingvegas.com', None, None, 'http://www.mrgreek.com/', 'https://www.walgreens.com/locator/walgreens-12244+w+cactus+rd-el+mirage-az-85335/id=7026', 'http://www.mlfchildrenstherapy.com', None, 'http://www.boltfreshbar.com/', 'http://www.axiacuisine.com', 'http://www.stagheadbarbershop.com', 'http://nailsandspabybobbie.com', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.BarnettManagement.com', None, None, 'http://www.impressionstyle.com', None, '1592686939', None, None, None, 'http://www.ampm.com', '1592686954', None, 'http://www.cookiesbydesign.com', None, 'https://bhmanagement.com/communities/district-flats/', 'http://alteredegosalon.com', 'https://ad.doubleclick.net/ddm/clk/458685338;262921492;w', 'http://mcdermottsservicerepair.com', 'http://www.synergyteamaz.com', 'http://theilliniinn.com', 'http://brewsoncarson.com', 'http://www.hkcafemadison.net/', 'http://www.creamistry.com', 'http://www.madisonbuyeragency.com', '1592687006', 'https://www.desertautotrader.com', 'http://www.saliturocarpet.com/', None, 'https://www.take5oilchange.com/locations/oh/willowick-124/', 'http://pavecleaner.com/', 'http://nailtique.ca', 'http://www.vintage95.com', None, 'https://spa-escape.ca', 'https://www.jaguarchandler.com', 'https://gummiboutique.ca', 'http://www.balnea.ca', 'http://www.a1meatshop.ca', None, None, 'http://absolute-surfaces.com', 'http://govillagesquare.com/', 'http://www.loveandlaceaz.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'https://www.storagewest.com/facilities/gray-road/?utm_source=YelpCTA&utm_medium=referral&utm_campaign=gray-road-business', None, None, None, 'http://www.ultramobile.com', 'http://www.disasterpro.net', 'http://www.jpopelaw.com/', None, None, 'https://www.usps.com/', None, None, 'http://palmvalleyanimalclinic.biz', 'http://www.discounttire.com', None, None, 'https://ashleyhomestore.ca/pages/pickering', 'http://www.sunchain.com', 'http://www.javaworks.ca', None, 'http://caldensebakery.ca', None, None, None, 'http://www.houlihans.com/my-houlihans/pittsburgh-station-square?utm_source=yelp&utm_medium=organic', 'http://www.montageatpecosranch.com', 'https://from-the-roots-up-catering.business.site', 'http://www.citysniffersdogclub.com', 'http://kickstandcharlotte.com/', 'http://SweetSpotCandyLasVegas.com', 'http://www.thelotuswellness.com/', 'http://www.torotaxes.com/las-vegas-89102-1/?L=true', 'http://www.snapfitness.com/lasvegas6', 'http://www.kabutolakenorman.com', 'http://bimmerbenzautorepair.com', 'http://www.starbucks.com/store/9298/', 'http://www.baskinrobbins.ca/', 'http://heynoodles.com', 'https://www.eastcoastcollisionllc.com', 'http://www.bojangles.com', 'http://www.quiznos.com', 'http://www.javinos.com', 'http://www.starclinic.org', None, 'https://www.thebrick.com/pages/store-north-york', 'http://www.goldennugget.com/lasvegas/pool_thetank.asp', None, 'http://www.islandrayz-tanning.com/', 'http://allcityautobodynv.com', 'https://www.ediblearrangements.com/stores/2435-West-Highway-160-Tega-Cay-SC-29708', '1592687183', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.elopementlasvegas.com', 'http://www.mrhandyman.com/az/westvalley', None, 'http://calibercollision.com/locate-a-caliber-collision-center/rock-hill', None, 'http://www.passionnailsspa.com', None, '1592687205', None, 'http://www.bahamabucks.com/', None, 'http://www.srdlv.com', None, 'http://www.fingerprintinglasvegas.com', 'http://www.mrhero.com/', 'http://www.evpcoffee.com/default.htm', None, 'http://www.fiber.google.com', 'https://delconpestcontrol.com', None, None, 'http://farmhousehospitality.tumblr.com', 'http://www.updatetvandstereo.com', 'http://www.mystiquehairstudiolv.com', '1592687245', 'https://www.moes.com/find-a-moes/north_carolina/concord/295?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://www.stoneymountaingunsmiths.com', 'http://www.keithspestcontrol.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://tropicalsails.com', 'https://taco-machin-llc.business.site/?m=true', 'https://www.hilton.com/en/hotels/cltuthx-hampton-charlotte-uptown/?SEO_id=YELP-HP-CLTUTHX', 'https://www.crescentdental.ca', 'http://brewgarden.com', 'http://www.so-cal-az.com/', None, '1592687278', 'https://www.statefarm.com/agent/us/az/tempe/curt-garrett-vkrbw1ys000?cmpid=b7jp_blm_0006', 'http://www.gorentals.com/location/las-vegas', 'http://angelchirocenter.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.ylimo.com', 'http://tiongsonlaw.com', 'http://www.bestextensionsaz.com', 'https://sttimothymesa.org', 'https://www.mediweightloss.com/locations/henderson?_ppc=Z8FWKRXKT5', None, 'http://www.garrisonpub.com/', 'http://www.mgmoptics.com', 'https://www.delasalle.ca', None, 'https://www.furevermemory.com', None, 'http://www.drcrowell.com', None, 'http://www.arizonains.com/?cmpid=poeb_blm_0006', None, 'http://www.royalprestige.com/', 'http://www.loveisballooning.com', 'http://www.elburropgh.com/', 'http://99only.com/store/Glendale---67th/', 'http://alliancejiujitsulasvegas.com', 'http://www.vss-security-services.com/', 'http://herbalnailsparadisevalley.com', None, 'http://www.oakley.com/en/store-finder', 'http://www.actionpumpaz.com/', 'http://www.sweetsushi.ca', '1592687355', 'http://www.pepperyoga.com/', 'http://www.elementalwi.com', '1592687364', None, 'https://rainbowmuffler.net/auto-repair-shops-cleveland-ohio/w-130th-street/', 'http://www.achachyauto.com/', None, None, None, 'https://totallytanparma.business.site/?utm_medium=referral&utm_source=gmb', 'http://www.bigearlsbbq.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281359349&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://imspainmanagement.com/', 'https://www.subwaydecarie.com', 'http://www.quesada.ca', 'http://www.banfield.com/veterinarians/nc/charlotte/bky?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.rogercoxac.com', 'https://academytavernonlarchmere.com', None, 'http://www.cariboucoffee.com', None, 'http://www.wendys.com', 'http://www.wineryatwolfcreek.com', 'https://www.flemingssteakhouse.com/locations/oh/woodmere?utm_campaign=Fleming_Yelp&utm_medium=Display&utm_source=Yelp', 'http://www.firstandvine.ca', 'http://www.kyreneinternalmedicine.com', 'http://www.azsprinklerservices.com', None, 'http://www.swisschalet.com', 'http://arkmobilerv.com', None, 'http://www.qtavern.com', 'http://www.jungseed.com/JungGardenCenters.asp#sunPrairieGardenCenter', 'http://manchuwok.com', 'http://www.greencleanmaidsweb.com', None, 'http://www.banfield.com/veterinarians/nc/concord/ccr?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://chinahouseoakmont.com', None, 'http://www.timhortons.com/', None, None, None, None, 'http://www.muchoburrito.com', 'https://www.walmart.ca/en/stores-near-me/markville-mall-supercentre-3053', 'https://www.vipautoservicecenterlv.com/promotions', 'http://www.sirnasfarm.com/', 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID134', None, 'http://www.yyc.com/', 'http://www.wimpysdiner.ca', 'https://www.nevadawebsitedesign.com', 'http://www.billardshootersgolf.com', None, None, '1592687517', 'https://www.cricketwireless.com', 'http://www.capitalwindowcleaningllc.com/', None, None, None, 'http://www.youngeryouclinique.com', 'http://brioitalian.com/crocker_park_village.html', None, 'https://locator.chase.com/az/chandler/1155-s-arizona-ave?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.ecollegetimes.com', 'http://www.halleenkia.com/', 'http://www.cicis.com/locations/sc-rock-hill-1807-cherry-rd', None, None, '1592687570', None, 'http://elbuengustolv.com', '1592687580', 'http://www.whyprecision.com', 'http://www.steaknshake.com', None, '1592687593', 'http://seay-s.com/', None, 'http://baileysblindrepair.com', 'http://www.meineke.com', 'http://erbsvegankitchen.com', 'http://www.rollingpinbakeshop.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700022442116483&ds_s_kwgid=58700002597446513&ds_url_v=2', 'http://www.ampm.com', 'http://www.mrbrakelasvegas.com', None, None, 'http://www.desertjewelesthetics.com', 'https://www.cwsapartments.com/marquis-at-desert-ridge-phoenix-az/', None, 'http://www.ormdi.ca/', None, 'http://www.8ballbailbondslv.com/', None, '1592687654', None, 'http://lomaxentlv.com', 'http://www.cibc.com', 'https://www.bigdogcoffeeshop.com', 'http://www.johnsonfitness.com', 'http://www.comedorguadalajara.com', 'https://kfrf.ca', '1592687687', None, 'http://graciesthriftstore.com', 'http://www.greenleafpc.com', 'http://www.windsorwest.com', None, None, 'https://loanscanada.ca', 'http://citizensbank.com/', None, 'https://www.skywaterapartments.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=yelpCPC', 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=578', 'http://www.massageaddict.ca/mississaugameadowvale', 'http://www.carowinds.com', 'https://www.clubpilates.com/dtphoenix/', None, None, None, 'http://bicycleheaven.org', None, None, 'http://www.71americangrille.com', 'http://www.torcconstruction.com', '1592687765', 'http://www.stripsidecomics.com/', 'http://www.blackspadetattoo.com', 'http://www.waterfrontbistro.com', 'https://www.divineimageinktattoopiercing.com', 'http://www.apleasanthomecleaning.com', 'https://lasvegasliving.com/properties/chateau-calais/', 'http://www.hannabechmusic.com', None, 'http://www.theportershouse.com', None, None, 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', None, 'http://chase.com', None, '1592687821', None, 'http://www.schoolofimaging.ca/', 'https://ad.doubleclick.net/ddm/clk/458954930;262601723;l', 'http://www.stemp.com', None, 'https://www.cindynailscalgary.com', None, 'http://westplumbingllc.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89130/838054/', 'http://www.sundevilauto.com/locations/az/tempe/tempe-3', 'http://www.bolandsopenkitchen.com/', 'http://www.bellsports.com', 'http://www.panchosbakery.ca/index.html', None, 'http://www.honeysbeestro.com', 'http://www.knightsoundsdjs.com', None, None, None, 'http://www.pawn1st.com/locations/goodyear-az', 'http://jennifershairstudiobarbershop.com', 'http://www.crossfitnewyou.com', 'http://www.rolfssalon.com', 'http://www.starbucks.com', 'http://www.eatatunclejacks.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'http://www.lululemon.com/mississauga/squareone?cid=yelp', 'http://www.greatclips.com/', 'http://www.challengefitaz.com', None, 'http://southwestspecialists.com/', 'http://www.mullensbarandgrill.com', 'http://www.hhvc.vetsuite.com/Templates/PawPrints.aspx', None, None, None, None, 'https://www.desertfinancial.com/Home/BranchDetails?branchId=87', 'https://www.worldclassfitnessmoontwp.com', None, '1592687971', 'http://www.audicharlotte.com', 'http://www.phxelectricbike.com', 'https://www.williamhharding.com', 'http://townlinemovers.ca', '1592687988', 'https://carolinascuisina.business.site', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd?jp_cmp=rb/LocalListings/aff/branch/na', None, 'https://www.hairbyashmarie.com', 'http://www.palmmedicalgroup.com/', None, 'https://culalanoodle.business.site', 'https://www.pancakecafe.com/stoughton-location/', 'http://www.grandviewpointe.com/', 'http://www.luxuryrvsofarizona.com', 'http://www.kemp-attorneys.com', None, None, None, None, 'https://bishops.co/locations/charlotte-south-end/', None, 'http://www.bistro83.com', 'http://www.oyshilv.com', None, None, 'http://www.thekoffadg.com', 'http://sweetpeapetspa.com', None, None, 'http://wearevision.com', '1592688087', 'http://valleycargroup.com', '1592688094', 'https://phoenixuptownbarbershop.com', 'https://imaginecinemas.com/cinema/cf-promenade/', 'http://findlaymazda.com', 'http://oldvegastattoo.com', 'http://www.ohms2vapor.com', '1592688118', 'http://www.stayinnsuites.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/2/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://www.barefootbeauty.ca', 'https://www.mark-taylor.com/apartments/az/chandler/san-palmas/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.snootyfoxtattoo.com', 'http://www.villageinnrestaurants.com', None, None, None, 'http://www.potbelly.com/Euclid?utm_source=ExtNet&utm_medium=organic&utm_campaign=Yext', 'http://www.adogslifelv.com', None, 'https://vegasstrongmovers.com', 'http://www.khaugully.ca', 'http://www.theboudoircafe.com', None, None, None, None, None, None, '1592688209', 'http://littlecitycoffee.net', 'http://InOutChiro.com', 'http://www.portofsubs.com', 'http://www.kravelasvegas.com/', None, 'http://www.lapetite.com/your-local-school/scottsdale-az-7177/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, 'http://www.eddiesplacerestaurant.com', None, None, None, 'http://www.footersdrycleaners.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.picttheatre.org', 'https://www.desertfoothillsdental.com', 'https://www.smithsurgery.com', None, 'http://www.cutsforpups.com', 'http://www.extremepita.com/', 'http://swingingdoorbar.com', 'http://www.alwaysopenlocksmith.com', 'http://bk.com/', 'https://www.autozone.com/locations/az/phoenix/3908-e-thomas-rd.html', 'http://www.activechiroandrehab.com', '1592688291', None, 'http://www.simplysmashingrageroom.com', None, 'http://www.phuketthaiaz.com', 'http://www.pitbullcriminaldefenseattorney.com', None, 'http://www.restorationhardware.com', 'http://millenniumendo.com', None, '1592688329', 'https://www.supercuts.com/locations/nc/matthews/sycamore-commons-haircuts-82122.html', None, 'http://www.southhillsauto.com', None, 'http://www.ferguson.com/branch/n-seventh-st-phoenix-az-plumbing', 'http://www.ihg.com', None, 'http://www.baskinrobbins.com/', None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.compassphoenix.com/', 'https://www.greatwolf.com/concord?loc=concord&utm_source=yelp&utm_medium=referral&utm_campaign=Concord&ctcampaign=7165&ctkwd=%7Bkeyword%7D&ctmatch=%7Bmatchtype%7D&ctcreative=%7Bcreative%7D&ctadpos=%7Badposition%7D', None, 'http://www.glenscustard.com', None, None, 'http://tenayaholistichealthcarecenter.weebly.com', None, None, 'http://www.gilaneh.ca', 'http://www.pinkadventuretoursscottsdale.com', None, 'http://www.statclinix.com', 'http://www.GuaranteedOfferHomeTeam.com', 'http://shop.brooklynclothing.com/', 'https://www.searshomeservices.com/locations/appliance-repair/az-phoenix/4604-e-cactus-rd', 'http://www.handandstonephoenix.com', None, 'https://www.abberlywoods.com', 'https://clevelandclearancecenter.com', None, None, 'http://www.cigna.com/cmgaz/locations/phoenix-central-multi-specialty-center', 'http://newyorkpizzaribs.com', 'http://www.azgolflessons.com', 'http://www.vitalant.org', None, 'http://www.alacrepes.com/', 'http://www.restaurantequipmentlasvegas.com', 'http://www.dsw.com/?cm_mmc=yelp-_-social-_-29190-_-main', 'http://www.loreto-apartments.com', 'http://www.shopstudio41.com', 'http://www.martiniskateandsnow.com', 'https://www.pnc.com/en/personal-banking.html', None, 'http://www.bruleriedesmonts.com', None, None, 'http://www.arizonalivescan.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.cherryontop.net/', 'http://www.upmc.com/Services/dermatology/cosmetic-skin/Pages/default.aspx', None, 'http://alexanderfunerals.com', None, 'https://arcpointlabs.com/las-vegas', None, 'http://www.westlibertysubaru.com', None, 'https://wildfire.sclv.com/en/Wildfires/Wildfire-Rancho.aspx', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_348', 'https://www.cyclegear.com', 'https://www.wyndhamhotels.com/hotel/02806?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:02806', 'https://doggystylezgrooming.com', 'http://www.prcevr.co', 'http://www.dresshaute.com', 'http://www.hairmotty.com', None, 'http://mrschickenaz.com', 'http://www.timhortons.com/', 'http://acguysinc.com', 'http://www.madfoxparty.com', 'http://www.byclaudiaspas.com', None, 'http://www.valleyking.com', 'http://www.suehair.com', 'http://1025grandchina.com/', None, 'https://www.bestwestern.com/en_US/book/hotel-details.03089.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessURL:03089', 'http://www.appalachianoutfitters.com', '1592688616', 'http://www.cutdle.com', None, None, None, 'https://www.relaxandrelief.club', 'http://www.torontooktoberfest.ca/', 'http://www.thegreenmango.com', 'https://www1.shoppersdrugmart.ca', 'http://www.rtfence.com', 'http://www.riosalado.edu/cafe', 'http://kegscorksandforks.com/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', 'http://www.shspros.com', None, 'http://www.solonohio.org/454/Community-Center-Member-Information', None, 'https://medmen.com/stores/#/north-las-vegas', 'https://www.indochino.com/showroom/scottsdale', 'http://www.cartridgeworldaz.com/', 'https://www.pteglv.com/locations/pts-gold/568-cactus-las-vegas-blvd/', 'http://www.bedbathandbeyond.com', None, 'http://www.rexall.ca/', 'https://www.wellishvision.com', 'http://dashengchinese.com', 'http://uglyducklingpilates.com', 'http://www.troyentertainment.com', None, 'http://www.charlottevideogame.com', 'http://www.chandleraz.gov/default.aspx?pageid=77', 'https://www3.hilton.com/en/hotels/arizona/pointe-hilton-squaw-peak-resort-PHXSPPR/index.html?SEO_id=YELP-HI-PHXSPPR', None, 'https://harumiyoga.com', 'https://local.albertsons.com/az/mesa/2727-n-power-rd.html', 'https://stores.petco.com/oh/beachwood/pet-supplies-beachwood-oh-1957.html?cm_mmc=PSH-_-Yelp-_-CCY-_-CCO-_-PET-_-AQU-_-Petco-_-Yelp2020-_-StoreListing-_-0-_-0', None, 'http://www.camclarkfordairdrie.com', 'http://www.hawgsdeli.com/', 'http://www.starbucks.com/store/6597/', 'http://richtree.com/locations/bayview-york-mills-north-york/', 'https://barrospizza.com', None, 'https://www.honeymee.com', 'http://www.artificialgrassrecyclers.com', 'https://airmagicllc.com', 'https://www.allgoodshutterandblind.com', 'http://www.cortabellas.com/', None, 'http://www.umamibbqsushi.com', 'http://iphixation.com', 'http://subway.ca', 'https://www.thewalkingcompany.com/shoe_store/292/nv/las_vegas/fashion_show_mall', 'http://brusters.com/robinsontwp/', 'http://superhardwoodguys.com', 'https://locations.timhortons.com/ca/on/richmond-hill/1070-major-mackenzie-dr.html', 'http://chineseculturalcentrecuisine.com', 'http://www.chiroinlasvegas.com', 'http://www.onthepathyardcare.com/', 'http://www.route69racing.com', None, 'http://www.ntb.com/store/6288/wadsworth-oh-44281-8754?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'https://www.cityhealthaz.com', None, 'http://www.allergyallegiance.com', 'http://www.lowes.com/', 'http://www.eq3.com', None, 'http://www.iPaintArizona.com', None, 'http://www.akronderm.com', 'http://allcareautomotive.com/', 'https://www.bathfitter.com/location/charlotte/', 'http://www.pghdentalspa.com', 'http://www.pinevalleyohio.com/', 'http://www.curryandroti.com', 'http://www.rumblebeeInc.com', None, 'http://www.fireplaceplusltd.com', 'http://tasteitaly.com', 'http://talaveratempe.com', 'https://pateldentistpeoria.com', 'https://www.titan911.com', None, 'https://calgaryfootdoc.com', 'http://www.katieamezquita.com', 'http://www.kneadmewellness.com/', None, None, '1592688941', 'http://vapehousenc.com', 'http://www.raydanielsalonandspa.ca/', 'http://chatime.com/', 'http://www.royalliquormerchants.com/', 'http://www.yourpsychicmarie.com', 'http://www.enterprise.com/car_rental/deeplinkmap.do?bid=019&arc=YMPL100&cm_mmc=&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://www.lakeinezto.com', None, '1592688972', None, 'https://locations.visionworks.com/ll/US/NC/Pineville/11025-Carolina-Place-Pkwy', 'http://www.clevelandpickle.com', 'https://three30five.com', '1592688991', None, '1592688999', 'http://creamistryAZ.com', 'http://www.canyonelectric.com/', 'http://www.eastlandsuitesurbana.com', 'http://alphaembroiderylv.wix.com/alpha-embroidery', 'https://www.bbvacompass.com/USA/AZ/Chandler/4060-W-Ray-RD/', 'http://www.circusschoolofarizona.com', '1592689026', 'http://www.kagopa.ca', 'http://www.searsoutlet.com', 'http://www.minicleveland.com', 'http://www.youmoveme.com/us/madison?utm_campaign=yelp&utm_medium=ubl&utm_source=madison', None, 'https://www.drparson.com', '1592689051', '1592689055', 'https://www.verizon.com/home/storelocator/pa/pittsburgh-15206/', 'https://www.thecommonerrestaurant.ca', 'https://fsyfitness.com/pressedjuicery', 'http://www.arizonafoot.com', 'http://www.policechaselv.com', 'https://agents.allstate.com/yvette-beck-las-vegas-nv.html', 'http://www.fountainofyouthsalonspa.com', None, 'http://www.foodlion.com', '1592689095', 'http://peterpiperpizza.com/', None, 'http://www.runningroom.com', 'http://www.starrlimos.com', 'http://www.toppropertyshop.com', 'http://Breastfeedingsupportlv.com', 'http://oftheearthwellness.com', 'http://www.lasvegasrockcrawlers.com/', 'http://www.edwardstreet.ca', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', 'http://www.communityreelartscenter.org', 'http://stagioniclt.com', 'http://www.urbannestnc.com', None, 'https://www.sephora.com/happening/stores/las-vegas-venetian', 'http://21streetcoffee.com', None, None, 'https://locations.fatburger.com/united-states/nv/texas-station/2101-texas-star-ln', 'https://www.walmart.com/store/2050/henderson-nv/details', 'https://stores.dickssportinggoods.com/oh/westlake/170/', None, 'http://www.printsmartaz.com', 'http://piazzetta.ca/', '1592689182', 'http://www.NevadaBusinessFurniture.com', 'http://www.nynyhotelcasino.com/entertainment/bars/center-bar.aspx', 'http://chinabuffetcharlotte.onlunchroom.space', 'http://www.live-parkside.ca', 'http://www.eattfood.com', 'http://www.beefobradys.com', 'https://www.apexdentalpa.com/dr-noel-fuller-endodontist', 'http://cnty.com/centurydowns', 'http://www.torontorestaurants.com/messis', 'http://www.goldenruletattoo.com', 'http://www.kensington-massage.ca', None, None, 'http://www.hotyogawellness.com/brampton/', 'http://www.goodwillswpa.org/', 'http://www.DottiesCupcakery.com', 'http://www.pizzahut.com/', None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.a1mississaugaauto.com', 'http://www.commonsort.com', 'https://songhuongyyc.square.site', 'https://www.hilton.com/en/hotels/cltwcdt-doubletree-charlotte/?SEO_id=YELP-DT-CLTWCDT', 'http://www.shannicakes.com/', '1592689277', 'http://www.sonoranlandesign.com', 'http://www.danriceteam.com', 'http://www.devicepitstop.com', 'http://www.goodyeardentistry.com', 'https://www.sanctuaryoncamelback.com/dining/jade-bar/', 'https://www.bigprintinglasvegas.com', 'http://www.rencoroofing.com/phoenix', None, 'http://krispykreme.com/location/avondale', None, None, 'http://local.firestonecompleteautocare.com/arizona/mesa/1840-n-lindsay-rd/?lw_cmp=IYP_YPC_MLP_349492', 'http://www.jackdishplumbing.com', None, 'http://www.haggen.com', 'http://www.cuttingedgecurbing.com', 'http://locations.michaels.com/az/mesa/2778/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'https://www.esso.ca/en/gas-station/mississauga-on-melandesso-200302255', 'http://shady-hill-chiropractic-clinic.business.site', 'http://www.protreelv.com', 'http://www.kobeherolkn.com/', 'http://www.hanaramenlv.com', 'https://ad.doubleclick.net/ddm/clk/434342171;236814625;b', 'http://www.livinglightingonking.com', 'https://www.autozone.com/locations/az/gilbert/734-w-warner-rd.html', 'https://jeremyhouse.com', 'http://santecares.com/locations/sante-of-mesa/', 'http://swensonfootankle.com/', None, 'https://www.cash1loans.com/Locations/NEVADA/Las-Vegas-Cheyenne.aspx', None, 'http://www.smilestartersdental.com/', 'http://Nookmadison.com', '1592689398', 'http://www.chispa.ca', None, 'https://cashtime.com/loan-center-details/3241-e.-mcdowell-rd.-phoenix-az-85008', 'http://nvlocksservices.com', 'http://www.thesummitatsunridge.com', '1592689418', '1592689422', '1592689426', None, 'http://www.cutterscottage.com', 'http://www.customlocks.ca', 'http://www.dontortaco.com/', None, None, 'http://thebeverlyhairsalon.com', None, None, None, 'http://www.mycorestudios.com', 'http://www.railexplorers.net', None, None, 'http://wefixuglypools.com', None, 'http://centerforscienceandwonder.org', 'http://www.petvalu.com', 'https://www.chick-fil-a.com/westgate', 'http://www.pizzapizza.ca', 'http://hallmark.com', None, 'http://www.tomscamperland.com/toms-camperland-mesa/', 'http://santropezapartmenthomes.com', 'http://www.purekneadmassage.com', None, None, 'http://reboundwest.com', 'http://www.ntb.com/store/8548/pittsburgh-pa-15236?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'https://www.walgreens.com/locator/walgreens-1745+e+southern+ave-tempe-az-85282/id=1197', 'http://callmetalman.com', '1592689538', 'http://www.quiznos.com', 'http://www.tozereyecenter.com/', 'https://www.hilton.com/en/hotels/stbohhx-hampton-suites-cleveland-southeast-streetsboro/?SEO_id=YELP-HP-STBOHHX', 'https://bangkokburi.com', 'http://powertrainautomotive.com', 'http://www.banfield.com/veterinarians/az/scottsdale/scd?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://www.popeyes.com/store-locator/store/restaurant_84967', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, None, None, 'http://www.lasbrisasnightclub.com/', '1592689581', 'https://backneckrehab.com', None, 'http://stroseanimalhospital.vegas', 'http://www.starbucks.com/store/9298/', 'http://contigoperuaz.com', None, 'http://www.horizonlighting.net', 'http://www.mycenters.com', 'http://mowpoweraz.com', None, 'http://www.bexleyvillageconcordmills.com', 'http://purplegurls.com', None, None, None, 'http://www.sonyastherapeutictouch.com', 'http://www.calgarylabservices.com/', 'http://www.monarkhome.com/showrooms/las-vegas', 'http://www.entirelypure.com/', 'http://www.facetfoundryjewelry.com', 'http://www.seanearlyphysicaltherapy.com', 'http://www.quiktrip.com', None, 'http://www.marsellaspizza.net', 'http://www.rbxhub.com', None, None, 'http://www.kerrendo.com/', None, 'https://locations.costavida.com/costa-vida-43d48f8a3aab', 'http://thestandardon29th.com', 'http://www.thegridgg.com', 'http://www.fallasstores.com', 'http://www.dunkindonuts.com', 'http://www.dominos.com', 'http://www.fantasticsams.com/pages/FindASalon/findsalondetail.aspx?SalonId=7179', '1592689712', None, 'https://scottsdaleps.com', 'http://www.cupidswedding.com', 'http://www.cheeselovehappiness.com', 'http://haircutmenwinstonchurchillmeadowvalemississaugaon.ca', 'http://xtremesushi.net', 'http://autofit.bz', 'http://www.sirackirealty.com', None, None, 'http://johnnysitaliandining.com', 'https://www.jiffylube.com/locations/nc/gastonia/3150', 'http://courtesyimports.com', 'http://www.intuitivetouchmassagebyjon.com', None, 'http://www.inzandoutz.com', 'http://www.steaklasvegas.com/', None, 'http://www.superstarcarwashaz.com', 'http://www.superpho.ca', 'http://www.haymakermarket.com', 'http://www.nybbaz.com', None, 'http://cccckids.com', 'http://www.covellilaw.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.arizonahardscapes.com', 'http://www.mollymcghees.com/', 'http://www.davecanfixyourcar.com', 'http://www.hollisgermannmusic.com', 'http://www.buffalowingsandrings.com/locations/charlotte', 'https://locator.chase.com/az/goodyear/767-s-cotton-ln?jp_cmp=rb/LocalListings/aff/branch/na', '1592689826', None, None, 'https://www.choicehotels.com/wisconsin/madison/clarion-hotels/wi103/rates', None, 'http://www.nichecoffee.ca', 'http://lovingpawspetclinic.com', 'http://waxhawescape.com', 'http://1300bridgeview.com/', 'https://www.goldengait.com', 'https://insomniacookies.com/locations/store/1148', None, 'http://www.lolitarestaurant.com/', 'http://www.parkscharlotte.com/', 'https://www.walgreens.com/locator/walgreens-4949+w+chandler+blvd-chandler-az-85226/id=3531', 'https://www.brilliantaz.com', None, 'http://www.highparkdentalcare.com', None, 'http://www.eatatnakama.com', 'http://glasshomeinspections.com', 'http://handymaninjacksonville.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, '1592689917', 'http://www.spoonandfork.ca/oakville.php', 'http://www.banfield.com/veterinarians/oh/willoughby/wll?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.ritzcarlton.com', None, None, 'http://www.asimplelifelasvegas.com', 'http://www.vanguardlv.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-paradise-valley?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-paradise-valley', 'http://timtatman.com/home', 'http://www.penn-station.com/', 'http://www.topsnbottomsfrozenyogurt.com/', 'http://www.champaignprinting.com', None, 'http://www.doylewallace.com/', None, 'http://thejerk-spot.com', '1592689989', 'https://www.tireworks.net/locations/4700-w-craig-rd-north-las-vegas/', None, None, None, None, None, 'https://sunsetstation.sclv.com/Dining/Sonoma-Cellar?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', None, None, 'http://www.paisanobarbershop.com', 'http://www.lagourmandinebakery.com', 'http://autodream.ca', 'https://stores.thenorthface.com/ON/VAUGHAN/CAN1260/', 'https://www.mrhero.com/hero_locations/index.php', 'http://www.ppcpizza.com/', 'http://www.snapfitness.com', None, 'http://dnahomegroup.com', 'http://nailstodaylv.com', 'http://www.charliesphoenix.com', 'http://www.petitepartystudio.com', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreID=62', 'http://www.peakpoolplastering.com', 'http://www.cocos-closet.ca/', 'http://maverickcoffee.com', 'http://www.scruffymurphys.ca/', 'https://www.home365.co/las-vegas', 'https://www.aqua-tots.com/old-town-scottsdale', None, 'http://trump.to/suits-yp', 'https://www.alittlewhitechapel.com', 'https://www.marcs.com/stores/marc-s-midtown-grocery-store-44134', 'http://www.thehousebrasserie.com', None, 'https://cortland.com/apartments/cortland-arrowhead-summit/', None, 'http://www.mypoolprovider.com', 'http://foxtheatre.ca/', 'https://thomasmidtown.com', 'https://skyharbor.com', 'http://www.axecapoeira-to.com', 'http://fyzicalpilates.com', 'http://www.paulsbookstore.com/', 'http://www.econrads.com', None, 'http://unwind-knitting.com/', 'http://BluBurger.com', 'http://www.chill-icecream.com', 'http://www.menchies.com/', 'http://roystrees.com', 'http://www.seasonaladventures.com', None, 'http://overbekedriving.com/', None, None, 'http://www.madisonavenuepub.com', '1592690176', None, 'http://theheightseventcenter.com', 'http://www.theartisanbakers.com', None, 'http://silverleafdayspa.ca/', 'http://www.thedistrictatgvr.com/carousel.php', None, 'http://www.rolibertosmexicanfood.com', 'http://www.stanleysfishaurora.ca/', 'http://www.clearvisioneyecenters.com', None, 'http://www.emmajeansrelics.com', 'http://www.vegashotspots.com', None, None, 'https://www.state48brewery.com', 'http://www.morningstarturf.com', 'http://www.ihg.com/holidayinn/hotels/us/en/montreal/yulcd/hoteldetail', 'http://www.fiestadentalcare.com', 'https://www.thirstydogflats.com', None, 'https://naturaldry.com', 'http://www.desertpita.com', 'https://www.parkmgm.com/en/restaurants/bavettes.html', None, 'http://wearehygge.com', 'http://www.elephantbar.com', None, '1592749022', 'http://www.gumbyspizza.com/', None, 'http://www.theyogisden.com', 'http://www.tandoorpgh.com/', None, 'http://www.chefdirect.vegas', 'http://www.glamsquadshop.com', 'http://www.bankofamerica.com', 'http://www.Ricosacai.com', 'http://www.lvbankruptcy.com', None, 'https://www.donatos.com/locations/hudson', 'http://strikerspool.ca', None, 'http://firstdentalofhuntersville.com/', 'http://www.CSLGLV.org', 'http://baconboystruck.com', 'http://www.arcadiayachtclub.com/', 'https://www.mrelectric.com/las-vegas', 'http://www.bibimkitchen.com', 'http://www.ontrac.com', 'http://www.beingbugged.com', 'http://www.nerolisalonspa.com/location/madison/', 'http://www.zorrosrestaurant.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.todaycommercialnews.com/', None, 'http://mooneystowing.com', 'http://www.modernfamilydentistry.com/', None, 'http://www.angeloshomestyle.com', 'http://www.appleautoglass.com/windshield-repair-replace/ON/Markham.aspx', None, 'http://www.starvingartistbar.com', 'http://www.moxiemercantile.com', 'http://www.99centssushi.ca/', 'http://www.myemeraldroof.com', 'http://www.herauralash.com', None, 'http://www.streetdanceacademy.com/index.html', 'http://www.calphalon.com/', None, None, 'http://www.cavalcadeauto.com/', 'http://www.woodiesautoservice.com', None, None, 'https://www.wyndhamhotels.com/hotels/48892?tel=18885959874&iata=00065402&cid=fe:gn:20160201:yl:pp:gn:48892', 'http://www.naturally-nurturing.com', 'http://www.TheMosquitoGuard.com', 'http://www.gamestop.com', 'https://www.walgreens.com/locator/walgreens-15514+w+waddell+rd-surprise-az-85379/id=7933', 'http://www.lovettsbodyshop.com', 'http://www.arizonafederal.org', 'http://www.journeys.com', 'https://www.oemesapawnshop.com', 'https://www.labanane.ca', 'http://coastersbarandgrill.ca', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.silkmedspa.ca/', 'http://insurance-agency.amfam.com/NV/matthew-meron/default.aspx?sourceid=agp0001027506', None, 'https://www.cityworksrestaurant.com/orangevillage/', 'http://www.waterandiceahwatukee.com/', None, None, None, 'http://www.sleepingbeautyaz.com/', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=0629', 'http://www.gielgaragedoors.com', 'https://www.skinfactorytattoo.com/las-vegas-tattoo-shop/', 'http://www.blackmarkettoys.com', None, 'https://www.iprophoenix.com', 'http://www.mylapels.com/gilbert', 'http://www.sallybeauty.com/', None, None, None, 'http://www.zauq.ca', None, None, None, None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://sushi-ten.com/', 'https://www.simonmed.com/locations/all/simonmed_imaging___stadium_village', None, 'http://www.greatclips.com/', None, None, 'http://www.amazonwindowtinting.com', None, None, None, 'http://www.shedsbuiltright.com', None, 'https://www.azuldesignlandscape.com', 'http://www.mindbodyandflow.com', 'http://www.middlefieldohio.com/recreation-parks-2/parks-2/eagle-park-2/', 'http://foamhome.co', None, 'http://www.quiltique.com', 'http://www.thesparitual.com', 'http://www.planetorganic.ca', 'http://www.momdocwfw.com/estrella', 'http://www.hollywoodlanes.com/', 'https://www.lasvegas.va.gov/locations/Northeast_Primary_Care_Clinic.asp', 'https://simplyshuttersshadesandblinds.com', 'http://www.anaturalcleaning.com/', None, 'http://www.thewoodstone.com/', 'http://www.timhortons.com/', 'http://www.studionorthyoga.com', 'http://www.diamondkitchenandbath.com/', 'http://sonoranlifesolutions.com', None, 'http://www.votsmd.com', 'https://www.chemdry.com/sunrise.az', None, 'http://www.walmart.ca/en/etobicoke-supercentre/3031', 'http://massageaddict.ca/maple', 'http://pandora.net', 'https://t-buds.com', None, 'http://www.hcpnv.com/clinic/northrainbow/', 'http://www.lubetown.com/index.html', 'http://www.wqflooring.com', 'http://www.bonniesprings.com', 'https://www.walmart.com/store/2603/gibsonia-pa/whats-new', 'http://swoozies.com/', None, 'http://www.imgonnafixit.net', 'https://www.hilton.com/en/hotels/sctrwhx-hampton-suites-scottsdale-riverwalk/?SEO_id=YELP-HP-SCTRWHX', 'http://lakecityair.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.pizzahousecleveland.com', 'http://www.vintagebymisty.com', 'https://www.kibosushi.com', 'https://www.autozone.com/locations/az/scottsdale/7401-e-mcdowell-rd.html', None, None, 'http://www.teslamotors.com', '1592749417', 'http://www.chinitamexicangrill.com/', None, 'http://winkinglizard.com/', 'http://www.timhortons.com/ca/en', 'http://www.holychuckburgers.com', 'https://sabai-nails-salon-spa.business.site', 'http://shoppesatriversedge.com/', None, None, 'http://saucissoncleveland.com', 'http://www.usstoragecenters.com', 'http://www.CommercialCleaningAz.com', 'http://www.MoonValleyHealth.com', 'https://www.petsmart.com/stores/us/oh/north-olmsted-store0529.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', None, 'https://sawescaperoom.com', 'http://glendalenails.com/', 'http://vfoutlet.com', 'http://www.enviroguardpestcontrol.com', 'http://www.quiktrip.com/', None, None, None, None, 'https://www.tourbillon.com/en/stores/las-vegas/', 'http://www.paramountfinefoods.com', 'http://www.potbelly.com/UW?utm_source=ExtNet&utm_medium=organic&utm_campaign=Yext', 'http://carolinesignaturesalon.com', None, 'http://www.concertproperties.com/rentals/one32', None, 'http://www.dollargeneral.com/', None, 'http://www.medicalmarijuanacardarizona.org', 'https://www.castletoysandgames.com', 'https://order.papamurphys.com/menu/papa-murphys-greenway', None, 'https://www.walgreens.com/locator/walgreens-2363+s+lindsay+rd-gilbert-az-85295/id=5215', None, 'http://www.vegasvalleyhomepro.com', 'https://www.saltlady.com', 'http://www.Gimikdalounge.multiply.com', 'http://www.uphillwireless.com', 'http://www.yorkmillsgallery.com', 'http://rightchoiceautomotive.com', None, 'https://monster-mobile-mechanic.business.site', 'http://dennystransmission.com', 'http://www.goodfeet.com/phoenix-glendale-az', 'http://oretta.to', 'https://www.honeysucklegelato.com/charlotte-nc-optimist-hall', None, 'https://www.originalmattress.com/store/67/South-Hills-McMurray-Pennsylvania-Store', None, None, None, None, 'http://www.1worldmedicine.com', None, None, 'http://www.kenthansenplumbing.com', 'https://mymhcommunity.com/Communities/Arizona/CasadelSolResortWest/?utm_campaign=Yelp_Directory_Listing&utm_medium=directory&utm_source=Yelp', 'https://southpointcasino.com/casino/sports-book/?cid=ypsb', 'http://www.elmar.com', 'http://www.triple7movers.com', None, 'http://newcanadians.hhstores.ca', 'http://www.elgueromexicangrill.com', None, None, 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/etobicoke-(1).aspx', 'http://www.arizonagamerslounge.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.hilightessence.com', 'http://www.greekvillagegrill.ca/', 'http://www.picknsave.com', 'https://www.loves.com/locations/659', None, 'http://www.wcui.edu', None, 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.muncheez.ca', None, 'https://www.puppyheaven.com', 'http://fixmyrvaz.com/', 'https://www.habithairculture.com', 'http://www.gourmetbistro.ca', 'http://www.woodystoronto.com/', 'http://www.tempemetro.com', 'http://www.bahnthaispa.com', 'http://www.kixxshoes.com', 'https://chatters.ca/stores/chatters-square-one/', 'http://slslasvegas.com/venue/the-sayers-club', None, 'http://www.vglasvegas.com', 'http://www.foamexpertsroofing.com/', 'https://www.b1locksmith.com', None, None, 'http://www.waterbeancoffee.com', None, 'http://www.lawngnomepublishing.com', 'http://www.gosfm.com', 'http://www.4thetruck.com', None, None, 'http://www.flairrestaurant.com', 'http://www.gyroinyourface.com', 'http://www.croshawspies.net', 'http://www.avalonhairdesign.ca', 'http://www.assembli.ca', None, None, 'http://cobblers-corner.ca', 'http://www.wac-it.com', None, None, '1592749688', None, 'http://www.turnofeventsproductions.com', 'http://www.coveryourglass.com', 'http://www.konagrill.com/locations/scottsdale-az', 'https://locations.mrtire.com/pa/monroeville/2680-mosside-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, None, 'http://www.pureimagephotobooth.com', None, 'https://aawl.org/content/how-adopt-dog-or-cat', 'https://www.burgersacehardwarementor.com', 'http://www.osbornejewelersinc.com', 'http://streetcoffee.net', 'http://www.planetfitness.com/gyms/champaign-il-772?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.thelittlevegaschapel.com', 'http://www.montanas.ca', 'http://www.caninecafe.net', 'http://www.upmc.com/services/urgent-care/locations/pages/robinson.aspx?curloc=&daddr=40.448825,-80.160499', None, None, 'https://www.circlek.com/store-locator/us/rock-hill/1839-celanese/2708401', 'http://www.mattsmithpt.com', 'http://www.timnelsonconstruction.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, None, 'http://www.clevelandairport.com', 'http://www.jimmythegreekgroup.ca', 'http://www.cibolaapartments.com', None, None, 'http://www.allianceglassaz.com', None, None, 'http://barnoneaz.com', '1592749776', None, 'https://www.suncoastdentalaz.com', 'http://www.gryphonaz.com/', 'https://www.wingstop.com/location/wingstop-979-north-las-vegas-nv-89032/menu', 'http://bqmburger.com/king-west', 'http://www.artoftuscany.net', 'http://shootersvault.net/', 'http://www.harveys.ca/', 'https://www.firehousesubs.com/locations/az/dana-park', 'http://www.petcareclinics.net', 'http://mariofazios.com', 'http://www.bagelworld.ca/locations.html', None, 'http://www.ranchorelaxotogo.com', 'http://www.uptowncyclescharlotte.com/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZSV', 'http://www.venetian.com/BRADY.aspx', 'https://www.hitchedlv.com', None, 'http://www.azmctowing.com', 'http://thebobgc.com/', 'http://www.wetseal.com', None, 'http://nothingbundtcakes.com/bakery/NC/matthews?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=matthews_291', 'http://www.babboitalian.com/', None, 'http://www.asskickin.com', 'http://www.jade-ballantyne.com', None, None, None, None, 'http://www.centro.ca', 'https://www.ulta.com/stores/las-vegas-nv-301', 'http://www.hotelblackfoot.com', None, '1592749874', None, 'http://www.hobbyshopofelyria.com', None, 'http://www.trolleypub.com/madison', None, None, 'http://www.rockandreillys.com', 'https://www.calgarycoop.com/stores/shawnessy/', 'https://www.admtl.com/fr/node/10556', 'http://www.myitea.ca', 'http://irrigationmdnc.com', 'http://www.salonlethomas.com', 'https://heroburgers.com/locations/york-university/', 'http://www.williamwilsonclothing.com/', None, None, 'http://www.timhortons.com/', '1592749925', None, None, None, 'http://www.boccaccioristorante.com', 'http://www.arbys.com', None, 'http://www.bikiniwaxing.com', '1592749956', None, '1592749960', None, 'http://www.happyvalleydentistry.com', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://patsysmarket.net', 'http://www.dunkindonuts.com', 'http://kamerynrose.com', 'http://www.aaa.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006435131504&ds_s_kwgid=58700000444951858&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', None, 'http://iamaflowerchild.com/locations/phoenix/', 'http://oralsurgeryphoenix.com', 'http://www.simpleelectricaz.com/', 'http://www.mattressfirm.com', 'http://www.pandoralv.com', 'http://www.melmedcenter.com', None, 'https://www.holidayrental.com', 'http://www.tk9o.com', 'http://www.costco.com/WarehouseLocatorDetailsView?callingPage=WarehouseLocatorView&storeId=10301&BeginAddress=J7H+0A1&langId=-1&location=J7H+0A1&warehouseNumber=546&catalogId=10701&numOfWarehousesToReturn=null', None, None, None, 'http://lifesphoto.com', None, None, 'http://highpointshop.com/', None, 'http://highlightsnailsspa.com/', '1592750045', 'http://www.vintagemodernfilms.com', None, 'https://www.target.com/sl/new-tampa/1382', None, None, 'http://www.starbucks.com/store/9298/', None, 'https://www.hallofframes.com', 'http://www1.tjmaxx.com', 'http://cervicalspinecenters.com', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/calgary-3315-32nd-avenue-ne.aspx?storeid=12&code=pc', 'http://www.AntiqueAlleyMall.com', 'http://www.civettacharlotte.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.bostonpizza.com', 'http://www.luckystrikesocial.com/locations/phoenix/', None, None, 'http://www.34easystreet.com/', '1592750119', 'http://www.baumanrarebooks.com', 'http://www.satayhutaz.com/', 'https://www.diautorepair.com', 'http://laserhair-removal-toronto.ca', 'http://www.bestbuypoolsandspas.com', 'http://www.pdqstores.com/gmaps/Wisconsin/MadisonArea/135.html', None, 'http://www.drtristasmiles.com', 'http://www.partellpharmacy.com', None, 'http://mcmurraydrycleaning.com/', None, 'http://encantadaliving.com/canyon-trails/', None, None, None, 'https://az.aaa.com/agent-office-locations/az/peoria/aaa-peoria-office', 'http://www.rossstores.com/', None, None, 'http://www.myprolific.com', None, 'https://meadowsfamilydental.com', 'http://bulldog-locksmith.com/locksmith-mesa-az', 'http://www.sukoshi.com', 'http://masseysrestaurant.ca/', 'http://www.alibabas.ca/index.php?route=common%2Flocation_details&loc_id=1', 'http://www.ecocarpetcleaning.ca', 'http://www.doughmamapizza.com', 'http://www.centerforlivingwell.org', 'https://locations.timhortons.com/ca/on/oakville/494-dundas-st-w.html', 'http://www.miazas.com/', None, 'http://www.itsagrind.com/', 'https://www.sclv.com', None, 'https://tacoselpaisa.us', 'http://www.ballantynevillage.com/#/directions-map/4553277958', 'https://www.campkodiak.com/contact/', None, None, 'http://www.ourcreativeescape.com', 'http://sofiascafe.com/', 'http://compassaz.church', 'http://schools.ccsd.net/vanderburg', None, None, 'http://www.cocofrutti.com', '1592750287', 'https://www.marathonlawgroup.com', 'http://sweatbyjsf.com', None, 'https://www.brickhouseburgersbainbridge.com/menu.html', 'http://www.teriyakiexperience.com', 'http://www.poppyshomedecoraz.com', None, 'http://www.yellowbot.com/ahwatukee-barbers-phoenix-az.html', 'http://www.401miniindy.com', None, 'https://stores.carhartt.com/pa/west-homestead/235-west-bridge-street.html', None, 'https://www.mattressfirm.com/stores/az/tempe/mattress-stores-tempe-az-85283-6166.html', 'http://www.arizonapersonaldefense.com', 'http://www.grateandbarrel.net', None, 'http://www.madcityfrites.com/', 'http://www.clarkcountynv.gov/constable/lasvegas/Pages/default.aspx', 'http://nourish123.com', 'http://www.nervousdog.com/', 'https://www.buzzardsplace.com', 'http://www.poorboytermite.com', 'http://www.paysannegelato.com/', 'https://goo.gl/oq2f2R', None, 'http://www.azaffordablehandyman.com', None, None, 'http://www.hometownoxygen.com', None, 'http://www.advantagecarrentals.com/car-rental-Mississauga', 'http://redefy.com/Phoenix/home.aspx', None, None, '1592750403', 'http://whasn.com/main/doctors/20/16', 'http://www.sprint.com', 'http://www.az-arrowawards.com', None, 'http://www.lvsuperiorlawncare.com/', 'https://www.nandini.guru', 'http://www.playitagainsports.com', 'https://locations.mrtire.com/oh/chesterland/8097-mayfield-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://azukar-coffee.business.site/?m=true', 'http://autoparadiseaz.com', 'http://www.desertpinesrehab.com', 'http://www.kierlandgolf.com/', 'http://www.ascenthealth.ca/', 'http://www.holidayinn.com/hotels/us/en/pittsburgh/pitmc/hoteldetail', 'http://www.arealocksmithlasvegas.com', None, 'http://www.jeffsbucketshop.com', 'http://www.ExploreVegasProperty.com', 'https://locations.usbank.com/index/arizona/gilbert/east-baseline-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'https://www.primroseschools.com/schools/west-chandler/?utm_source=yext&utm_medium=maplistings&utm_campaign=localmaps', None, None, 'http://www.chefwilliamturner.com', 'http://www.washhllc.com', 'http://www.turfdirectaz.com', 'http://www.centurylink.com/', 'https://toplinepest.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://crossfitnorthvalley.com/', None, 'http://www.mexicafeonliz.com/', 'http://dodeysbar.com', None, 'https://www.bigbudsflorist.com', None, 'https://www.cricketwireless.com', 'http://stylesforless.com/', 'http://radioshack.com', 'http://www.pinevilletavern.com', None, 'http://www.terraceafterhoursvegas.com', 'http://www.liberatechurch.com', 'http://www.addisonsinc.com/', 'http://www.pizzanova.com', 'http://www.epicthriftstores.com/?q=e003', 'http://www.kkvv.com', 'http://www.rulabula.com/', 'https://calibercollision.com/locate-a-caliber-collision-center/charlotte-tyvola-rd', 'http://www.allfiredupakron.com', 'http://www.mrsub.ca', 'http://www.mygennaros.com', None, 'http://www.mrsub.ca', '1592750590', 'https://www.windsorplywood.com', 'http://www.lexusofrichmondhill.com', 'http://www.thebeerstore.ca/locations/yongedundas', 'http://vanhornerestaurant.com/', 'https://wildfire.sclv.com/en/Wildfires/Wildfire-Rancho.aspx', 'http://www.visionsourcevegas.com', 'http://www.arizonaartsupply.com', 'https://www.carrabbas.com/locations/nc/south-end-charlotte?utm_source=yelp&medium=social&utm_campaign=location_listings', 'http://www.carrillolandscape.com/Home_Page.html', None, 'http://DollarTree.com/', 'http://www.sunstaterefrigeration.com', 'http://www.theamishhome.com', 'http://www.evymama.ca/', '1592750638', 'http://summerlinsmiles.com', 'http://www.shamrockfoods.com', None, 'http://www.muchoburrito.com', None, None, None, 'http://www.mystricklands.com/', None, 'http://www.ci.middleton.wi.us/DocumentCenter/View/895', None, 'http://heynoodles.com', None, 'http://midwoodsmokehouse.com', 'http://abovethecrustpizza.com', 'http://www.mindyashhypnosiscenters.com', 'https://locator.chase.com/az/tempe/4714-s-rural-rd?jp_cmp=rb/LocalListings/aff/branch/na', 'https://www.smartstyle.com/en-us/locations/nv/north-las-vegas/located-inside-walmart-2592-haircuts-3346.html', 'http://www.bigsonline.com', None, 'https://www.papamurphys.com/store-finder/position?utm_source=yelp&utm_medium=2018ads&utm_campaign=AZ034', 'http://www.mattressfirm.com/', 'http://fabrestaurants.ca/restaurant/dominion/', 'http://www.mywellnessdental.com', 'https://gunnellstiresandservice.com', 'http://www.lcbo.com', None, None, 'http://www.beautycollection.ca', 'http://www.onyxxsportsbar.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.pearlbridalhouse.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://blindbeggarpub.com/', 'https://www.mcalistersdeli.com/locations/nc/charlotte/9864-rea-road-suite-a-1237', 'https://www.pineapplehealth.org', None, 'http://www.ayurvedainpittsburgh.com', None, None, 'https://www.sunrisepreschools.com/locations/40th-st-ray/?utm_source=yelp&utm_campaign=online_listing_phoenix_271&utm_medium=referral&utm_term=business_url', 'http://www.zymages.com', 'https://www.haircutmenballantynepromenadenc.com', 'http://www.morso.me', None, None, 'http://www.marriott.com', 'https://www.autorepairshopchandler.com', 'http://www.zagaras.com', None, 'http://www.claimjumper.com', 'http://www.sierramovingsystems.com', None, 'https://www.tsplv.com', 'http://www.vegan-bites.com', 'http://perfecttouchnailandspa.com/', None, 'http://www.lawsonfamilyplumbing.com/', None, 'http://www.mirenasfashions.com', 'http://www.usareplacementautoglass.com', None, 'https://www.labsensecanada.com', None, 'http://redstarfoaminc.com', 'http://www.econrads.com', '1592750861', '1592750865', 'http://lvenrichment.com', 'http://shopselltrade.com/locations/mesa', 'http://www.bk.com', None, 'https://www.cellphonerepair.com/henderson-nv/', 'https://www.tidesatsouthtempe.com', None, 'http://www.jakescapellc.com', 'http://www.pinoyscoffeeandboba.com', None, 'http://www.thequiltcompany.com', 'http://www.davenporttempe.com', 'http://www.animalcremationservices.com', 'http://www.idoeventsllc.com', 'https://www.phoenix.gov/nsd', 'http://suburbansole.com', 'http://www.elementsunscreens.com', None, 'http://www.fireflycoffeehouse.com', 'https://www.choicehotels.com/arizona/phoenix/comfort-inn-hotels/az053/rates', 'http://www.revivalbiltmoreapts.com', None, None, 'https://www.radissonhotels.com/en-us/hotels/country-inn-rock-hill-sc', 'https://www.dominos.com', 'http://www.nevadaheart.com', 'http://www.raintreecountryclub.org', 'http://www.dreamimagesigns.ca', None, None, 'https://www.crumleyroberts.com', None, 'https://www.hudsonlibrary.org', '1592750980', None, 'http://rocketfizz.com/locations/rocket-fizz-cleveland-oh', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.walgreens.com/locator/walgreens-6435+aliante+pkwy-north+las+vegas-nv-89084/id=2590', 'http://www.bickfordbistro.com', None, 'http://www.azdhs.gov/vitalrcd/index.htm', None, None, 'http://buzzardcove.com/', 'http://www.activeeyecare.com', 'http://www.whiteninglounge.wordpress.com', 'https://crumblcookies.com', 'http://www.bk.com', None, 'http://local.fedex.com/ca_english/on/toronto/office-3402/', None, None, 'http://www.sallybeauty.com', 'https://www.dillards.com/stores/summit-mall-akron-ohio/0371', 'https://www.dunn-orthodontics.com', 'http://torisbakeshop.ca/', 'http://www.oasisconvention.com', 'https://www.masasushicharlotte.com', 'http://www.crcaz.com/adrienne.htm', 'https://www.parkmgm.com/en/restaurants/la-la-noodle.html', 'http://www.macys.com', '1592751077', 'https://www.WestwindWellness.com', None, 'http://www.amazingkeys.com', 'http://oldcarolina.com', 'http://www.zellers.com', None, None, 'https://www.starbucks.com/store-locator/store/6539', None, '1592751108', 'https://www.lakeviewcornercafe.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.downside-risk.com', 'https://www.libertytax.com/income-tax-preparation-locations/19248.html', 'https://www.davidsbridal.ca/?utm_source=Yelp&utm_medium=OrganicSearch&utm_term=400&utm_content=DisplayURL&utm_campaign=WebsiteListing', 'http://jjbeancoffee.com', 'http://www.wardbrodt.com', None, 'https://www.walmart.com/store/5497/evans-mills-ny/whats-new', 'http://www.acceptancerecoverycenter.com', 'http://www.athenastempledayspa.com', 'http://www.justremodel.com', 'http://www.show-us-your-tips.com', None, 'http://greasyaxle.com/', None, 'http://www.sabaideethaicuisine.com', '1592751171', 'https://nivexolegalforms.com', None, 'http://www.kidsrising.com', 'http://www.diehlofrobinson.com/', None, None, 'http://pizzabogo.com/', None, None, 'http://drstephengordon.com', 'http://www.yogenfruz.com/storelocator/store/3971/', 'https://madtownchickennfish.business.site/?m=true', None, 'http://www.greenlifewater.com', 'http://us.christianlouboutin.com/ca_en/', None, None, None, None, 'http://www.ecrew.vegas', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://goodyear.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.innonnegley.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.jerseymikes.com/2063', None, None, 'http://www.comfortinnpittsburgh.com/comfortinnpitt/restaurant.html', 'http://www.cleanfreakcarwash.com/', 'http://www.dccentre.ca/', 'http://www.bostonpizza.com', 'http://www.cindysalterations.ca', 'http://livingwellhomes.com/apartment-communities/greater-phoenix-az/azul', 'http://www.metromississauga.ca', 'https://www.dignityhealth.org/ourdoctors/1093712986-Raji-Venkat?utm_campaign=DignityHealthMedicalGroupNevada&utm_medium=Physician&utm_source=LocalSearch&utm_term=Raji-Venkat-1093712986a', 'http://www.quantumcoffee.io', '1592751301', 'http://www.midas.com/pittsburgh/store.aspx?shopnum=6140&dmanum=688', 'http://locations.jjill.com/az/chandler/413/', 'http://www.biggby.com', 'http://www.glendalesalathaiaz.com', 'http://azvr.com/', 'http://www.Stereo1.ca', None, 'http://ars.com/locations/Las-Vegas-NV.aspx?partnerName=Yelp&adName=Yelp_Paid&utm_source=Yelp&utm_medium=paid_listing&utm_content=Yelp_Paid&utm_campaign=YelpHVAC', None, '1592751335', 'http://www.peoriamedicalcenter.com', 'http://www.aztowne.com', None, None, 'https://us.petvalu.com/location/5176', 'http://ThePsychicGalleryOnline.com', 'http://www.aceofshadesaz.com', 'http://www.dieselrepairpeoria.com', 'https://www.carmax.com/stores/7244?adcode=YLP7244&utm_campaign=LG_AFF&utm_source=LG_AFF_YLP&utm_medium=local&utm_content=shop', 'https://homesmart.com/real-estate-agent/arizona/scottsdale/15694-chris-scott/Welcome', 'http://www.popsoda.com', None, 'https://www.maxcashtitleloans.com/?yelp', None, 'http://www.golfgilbert.com', None, 'http://meatandfish.com', 'https://locations.massageenvy.com/nevada/henderson/358-w-lake-mead-parkway-ste-100.html', None, None, 'https://stores.arhaus.com/oh/cleveland/7440-brookpark-road.html', 'http://www.frysfood.com', 'http://www.coolcuts4kids.com/salondetail/default.asp?salonid=66006', None, 'https://www.fincamadison.com', 'http://www.icehousetavernphx.com', 'http://www.chevron.com/', 'http://www.gcapa.net', 'http://www.aaa.com', None, 'http://www.badaboomaz.com', 'http://www.harperstire.com', None, 'https://locator.chase.com/oh/stow/4499-kent-rd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.justcatscleveland.com', 'http://valleywestmortgage.com', 'http://www.burgerspark.ca', 'http://exposedgallery.com', 'http://www.brendentheatres.com/palms-las-vegas-14/palms-info/', 'http://www.asapmobilervservice.com/asap/Contact_Us.aspx', 'http://happyvalleynailsandspa.com', 'http://www.tahitivillage.com/amenities/mahana-spa/', 'http://storelocator.staples.ca/stores/en_CA/ON/Etobicoke/12', 'http://locations.michaels.com/nc/charlotte/5032/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://coyotechiropractic.com', 'http://www.paintingwithatwist.com/pittsburgh-north/', 'http://www.BizzyKidzKabCompany.com', 'https://www.petsense.com', 'http://www.breakfastkitchenbar.com', None, 'https://www.walmart.com/store/5257/mesa-az/details', 'http://solonberrisoptical.com', 'https://www.publicstorage.com/arizona/self-storage-tempe-az/85282-self-storage/1100?pid=wyelp&CID=1245&CHID=AFL', None, None, 'http://www.petitfour.ca', None, 'http://www.southernaroma.ca/', 'http://www.suitdoc.com', 'http://surprisegolfclub.com/Home_Page.php', 'http://trolleyllama.com', 'http://olympianbarbershop.com', None, None, 'http://www.scottsdalemassageaz.com', 'https://www.ritasfranchises.com/GlendaleFoothills', 'http://fiesta-expresscare.com', 'https://www.rockboxfitness.com', 'https://stores.petco.com/pa/homestead/pet-supplies-homestead-pa-1811.html?cm_mmc=PSH-_-Yelp-_-CCY-_-CCO-_-PET-_-AQU-_-Petco-_-Yelp2020-_-StoreListing-_-0-_-0', 'http://fivestarroofingpgh.com', None, 'http://zorbasrestaurant.ca', 'http://www.ArcadiaDryCleaners.com/', None, None, 'http://www.framedewe.com', None, None, 'http://www.anexquisitemassage1.com', 'http://www.johnnymalloys.com/ourlocations/cleveland_oh.aspx', 'http://www.funtobefit.net', 'http://www.akropoliskafe.com/', None, None, 'http://www.opticianado.com', 'http://www.innerblissyogastudio.com', 'http://www.idealoverheaddoors.com/', None, 'http://www.mysimplygreen.com', 'http://patchinpictures.com/', None, 'http://www.nedautodetailing.com', 'http://www.sappororestaurants.com/', 'http://boloautorecovery.com', 'http://www.mammaspizza.com', 'http://www.madisonchildrensmuseum.org/', None, None, None, None, 'http://universalautomachine.com', 'http://mikisbarbersalon.com', None, None, '1592751684', 'http://www.desertendo.com/', 'http://www.eliteappliancesrepair.com', None, 'http://www.asianfusion168.com', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'https://shi-miaodao-yunnan-rice-noodle-restaurant.business.site', '1592751718', 'https://www.chilis.com', None, 'https://www.saigonnoodles.co', 'http://www.lexusofhenderson.com', 'https://www.missiondemolition.com', 'http://aquamanpoolcareLv.com', None, 'http://www.rawbeautybarinc.com', None, None, None, 'http://www.avondaleautoservice.com/', None, None, None, 'http://cityoftheworldlasvegas.org', None, 'https://www.purchasegreen.com/locations/phoenix-az/', '1592751788', '1592751791', None, 'http://library.vicu.utoronto.ca', 'http://twilliamspost65.org', 'http://www.menchies.com/frozen-yogurt-shops/frozen-yogurt-chandler-gateway-az', None, 'http://www.dynamicdieselrepairinc.com', None, 'http://www.jockey.com/location?store=129', 'http://www.the-plf.com', 'https://ad.doubleclick.net/ddm/clk/434417647;234991578;x', 'http://www.citytacosphoenix.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.jammielynnscleaning.com', None, 'https://www.ttc.ca/Subway/Stations/Warden/station.jsp', 'http://www.planetfitness.com/gyms/lorain-oh-1558?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.ilovedkdogs.com', None, 'http://www.chinainnorder.com', 'http://www.calicocorners.com/storepage.aspx?storeid=010', 'http://www.maharanaindiancuisine.com/', None, 'http://eighteeneight.com/north-scottsdale-az/?utm_source=yelp&utm_medium=organic&utm_content=weburl', 'http://www.arcadiawd.com', 'http://www.acupuncturephx.com/', None, 'http://www.certifiedcs.com', 'http://www.emmerlingicecream.com', 'http://www.fairmontpharmacy.com', 'http://www.banfield.com/veterinarians/oh/cuyahoga-falls/caf?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, 'http://atriumanimalhospital.com', 'http://www.barberahomeimprovement.com', 'http://www.boletsburrito.ca/', 'https://www.number1friedrice.com', 'https://wshomemaintenance.com', None, 'http://www.DentalCenterofCharlotte.com', None, 'https://www.spirithalloween.com/custserv/locate_store.cmd', 'http://www.northhillstreeservice.com', None, 'https://www.sutersspeedshop.com', 'https://f45training.com/ScottsdaleMidtown/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.azchironeuro.com', '1592751956', 'http://www.greatclips.com', None, 'http://www.azfeet.com/Location/Phoenix.aspx', 'https://www.cusd80.com/Domain/2039', 'http://phoenix-midtown.orangetheoryfitness.com', None, 'https://www.historicallandmarkpittsburgh.com', None, 'http://www.quipscafe.com', 'http://www.thewesterlyrestaurant.com/', '1592751993', 'http://radiancebanquethall.com', None, '1592752003', None, None, None, 'http://subway.com/', 'http://crowningglorytearoom.com', 'http://stumpgrindersinc.com', None, 'http://www.clonemykey.com', 'http://www.experiencedhomecleaners.com', 'http://www.sweetsunlimitedaz.com', None, 'http://carolinajerky.com', None, 'http://missionthriftstore.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.pittsburghsymphony.org/pso_home/web/mozart', 'http://www.thefrozenisle.com/', None, 'http://firstpersoncareclinics.org', None, '1592752071', None, None, '1592752081', None, 'http://www.paceprocarpetcleaning.com/', 'http://www.vostoronto.com', None, 'http://www.the-beeman.com', 'http://www.augustashpsllc.com', 'http://www.untohimlandscaping.com/', 'http://r-atv.com', None, 'https://tahitifusion.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://cardiogo.ca/locations/king-west', 'https://dutchbros.com/?utm_source=glendale&utm_medium=yelp&utm_campaign=website_glendale', 'http://ritosmexicanfood.com', 'http://www.nevadachickencafe.com', 'http://www.eyebrowsrus.com', None, 'http://www.prostarplumbingheating.ca', 'http://www.papersource.com', 'https://pinnacledancenorth.com', None, None, None, 'http://www.chelonco.com/', 'http://www.buonanottetoronto.com', 'https://store.vioc.com/pa/penn-hills/11690-frankstown-rd-15235-060062', 'http://www.themetroatzanjero.com', None, None, None, 'http://www.superstore.ca', None, 'http://www.clairbnb.com', 'http://chiropractorlasvegas-yenchiropractic.com/', 'http://gardunosrestaurants.com', 'https://www.discounttire.com/store/az/phoenix/s/1018?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.subway.com', 'http://www.thephxstudio.com', 'https://www.wellsfargo.com', None, 'http://www.delallosfortcouchcafe.com', 'http://mcdonalds.com/', 'http://www.jubileeprincesspartiesnv.com/', '1592752245', 'http://www.fairviewparkrec.com/bain-cabin-rental.html', None, None, 'http://pamperedpetsonwheels.com/', 'https://dealer.sprint.com/universal-wireless/find-a-store/256532-brighton-co-80601', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://www.waxcenter.com/az-phoenix-camelback?utm_source=yelp&utm_medium=cpc&utm_campaign=cQVpdviIJNkzO-5tFM_s9w', 'http://www.inssavers.com', None, None, None, 'https://www.desertfinancial.com/Home/BranchDetails?branchId=92', 'http://www.springmade.ca', 'http://www.nevadamattress.net', 'https://desertmountainwater.com', 'https://www.lopezeyeinstitute.com', '1592752309', 'https://www.gwresources.com', 'http://bestnailsnspaaz.com', 'http://www.matildascloset.com', 'http://www.hallierlaw.com', 'https://www.catawbaheightsanimalhospital.com', 'http://www.carolinaapplianceservice.com', None, None, None, 'http://iphonerepair702.com', 'https://nothingbundtcakes.com/bakery/NC/marvin?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=marvin_87', None, 'https://www.orderstart.com/chopstickuptown', 'http://www.activegreenross.com/tire-centre/richmond-hill#mapBox', 'http://lindosrestaurant.food-places.com', 'http://www.cjreuse.org', None, None, 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://www.vidaspalv.com', None, None, 'https://locations.dressbarn.com/nv/lasvegas/dresses-lasvegas-nv-719.html', 'http://www.mrautobodyinc.com', None, 'http://www.childrensstorefront.com', 'https://www.calgarycoop.com/stores/shawnessy/', None, 'http://toastcafeonline.com', 'http://www.enjoythestation.com', None, None, None, 'http://www.canadaglass.ca', None, 'http://scottsdalenailsandspa.com', 'http://www.pawsinthebath.com/home.html', 'http://vivefitness.com/etobicoke-south', None, 'http://www.theshirecafe.com', 'http://www.drtarabrodkin.com', 'http://www.docmindybeth.com', 'http://stores.sallybeauty.com/az/mesa/beauty-supply-mesa-az-3479.html', None, 'https://locations.dennys.ca/AB/CALGARY/248179', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXDO', None, 'http://www.crossfitsixthcity.com', None, None, 'https://locations.wendys.com/united-states/az/glendale/8273-w.-union-hills', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', None, 'http://www.leelovesyoga.com/', 'https://www.haircutmensouthendcharlottenc.com', 'http://stores.lanebryant.com/az/chandler/plus-size-clothing-chandler-az-4190.html', 'http://www.divorcelawaz.com/', 'https://www.storquest.com/self-storage/az/scottsdale/1439/', '1592752513', 'https://uglytunasushi.com', 'https://www.terrastaffinggroup.com/locations/phoenix/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.wwizard.com', 'http://www.decadentmacaron.com', 'https://www.ediblearrangements.com/fruit-arrangements?utm_campaign=StoreID559&utm_medium=Listing&utm_source=Yelp', 'http://www.bk.com', None, None, None, 'http://www.pizzapizza.ca', 'http://www.costco.com/warehouse-locations/se-gilbert-gilbert-az-644.html', 'https://www.wellsfargo.com', 'http://www.eliterepeatsshop.com/', 'http://www.electric-genie.com', 'http://www.myvegascars.com', 'http://www.monicagubler.com?cmpid=pu02_blm_0006', 'http://www.krispykreme.com', 'http://www.thrifty.com/?campid=DS:YL_THR_20150109_HP', 'https://www.desertgardenmontessori.org', None, 'http://www.alphamicropigmentation.com', 'https://www.dominos.com', None, None, 'http://www.happypetspalace.com', '1592758030', None, '1592758034', 'http://www.racewaycarwash.com', None, None, 'https://www.payless.com/stores-location/AZ-SCOTTSDALE-3761.html', 'http://www.wrightclinic.com', None, None, 'http://wokinus.com', 'https://www.goldengobletrestaurant.com', None, None, 'http://www.mattressfirm.com', 'http://www.executivecarpetservices.com', None, 'https://petersenpt.com/physical-therapy-in-tempe-arizona', 'http://www.jiajiamoving.com', None, '1592758091', '1592758095', 'http://www.nyonicouture.com', 'http://www.glenshawauto.com', None, 'http://www.drjlovessmiles.com', 'http://www.cucinalocale.ca/', None, None, 'http://www.wonderpens.ca', 'https://www.sheetz.com', 'http://www.herzig-eye.com', 'http://toughtimeslegal.com/', 'https://www.dillards.com/stores/carolina-place-pineville-north-carolina/0151', 'http://benetflorentine.com', 'https://local.safeway.com/safeway/az/phoenix/3132-e-camelback-rd.html', 'https://www.duluthtrading.com/locations/?city=Belleville&StoreID=004&street-address=1107RiverSt.', 'http://www.tallmadgeshipcenter.net', 'http://www.bearandthehoneyphx.co', 'http://milburnlawoffice.com/', None, None, 'https://rv.campingworld.com/dealer/charlotte-north%20carolina-concord', 'http://boanddeemoitsabullything.blogspot.com/', 'http://www.doodlebugs.com/', 'https://www.popeyes.com', 'http://www.go-gettersmovinglabor.web.officelive.com', 'http://www.tutortime.com/your-local-school/phoenix-az-6086/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'https://dutchbros.com/?utm_source=las-vegas&utm_medium=yelp&utm_campaign=website_las-vegas', 'http://www.sunbeltrentals.com', None, None, 'https://www.jgwentworth.com/lp/hl/yelp.html?leadSource=Phoenix', 'https://www.mattressfirm.com/stores/az/goodyear/mattress-stores-goodyear-az-85395-6648.html', '1592758213', 'https://www.hilton.com/en/hotels/clecchx-hampton-cleveland-airport-tiedeman-rd/?SEO_id=YELP-HP-CLECCHX', '1592758221', None, None, None, 'https://www.arizonabiltmoredentistry.com', None, None, 'http://www.shaanxibiangbiang.com', 'http://www.keystous.com', None, None, None, 'https://www.chilis.com', None, 'http://thelodgesasquatchkitchen.food-places.com', None, 'http://www.specelectriccompany.com', 'http://pathmakerplumbing.com', None, 'http://cmtaxcpa.com', 'http://la-actingacademy.com', None, 'https://ad.doubleclick.net/ddm/clk/434183253;236814625;f', 'http://www.cconfront.com/', 'http://www.vegasbrewscruise.com/', 'https://www.coppas.com', 'http://beer2beerinc.com', None, None, 'http://promptservicetoday.webs.com', 'http://www.paramountfinefoods.com', 'http://www.triumphpropertymanagement.com', 'http://www.thepaperheart.com', 'https://www.eyecontactmadison.com/locations/eye-contact-madison-west.html', None, None, 'http://www.loveandsandwiches.com', None, 'http://www.cupsandcakesaz.com', 'http://www.stardustnewmarket.com', '1592758346', 'https://ad.doubleclick.net/ddm/clk/434332343;236814625;b', 'https://www.metropcs.com', 'http://www.smoke-bbqgrill.com', None, 'http://www.cccnevada.com', None, 'http://www.cnanational.com', 'http://www.yourcharlotteconnection.com', 'https://phoenix.bondinvestigations.com', None, None, 'https://www.buffocalgary.com', None, None, None, 'http://www.allianceflooringsales.com/', None, 'http://www.lacresenta.net', 'http://www.sohosushiburrito.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://ad.doubleclick.net/ddm/clk/434322314;234989055;g', 'http://www.theredzonemadison.com/the-annex/', None, 'https://www.venetian.com/shops/the-atrium.html', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://www.summerschristmastreefarm.com', None, 'http://www.theoakstheater.com/', None, 'http://www.popnaillv.com', None, '1592758426', None, 'http://www.midas.com/pittsburgh/store.aspx?shopnum=6394&dmanum=688', 'http://www.freedomandtheseed.com', None, 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'https://www.crosseyedcricketpeoria.com', 'http://hennashoppe.com', 'http://reynaairconditioning.com', 'http://vegasminis.com', None, None, None, 'https://crm.pawfinity.com/south-point-pet-spa', 'http://sportsandfamilycareclinic.com/', 'http://www.brakemasters.com', 'http://www.camelbackbarbershop.com', 'https://www.weatherking1.com', 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', 'http://www.pitapitusa.com', 'https://www.pacificaseniorliving.com/nv/las-vegas/pacifica-senior-living-spring-valley/index.aspx', 'https://www.sprint.com/storefronts/bd/sprint-las-vegas-nv-89119-fcs-748/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://transportationmovers.com', 'http://www.fantasticsams.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.canadiantire.ca/en/store-details/on/warden-eglinton-on.store.html', 'http://www.woodlandveterinary.com', 'http://www.foreveryoungswimwear.com', 'https://www.azoffice.com', 'http://www.littlecaesars.com/', 'http://www.chem-dry.net/scottsdale.az', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.evos.com', '1592758505', 'http://www.azthriftiques.com', 'http://www.thed.com/party-scene/vue-bar/', 'https://www.hilton.com/en/hotels/phxcbes-embassy-suites-phoenix-biltmore/?SEO_id=YELP-ES-PHXCBES', 'http://www.hubertsteamcleaning.com', 'http://www.ilpostinorestaurant.com', None, 'https://locations.monro.com/oh/tallmadge/175-west-avenue?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://carolinafishmarket.com', None, '1592758530', 'https://clevelandmetroparks.com/parks/visit/parks/lakefront-reservation/edgewater-beach', 'https://www.state48brewery.com', 'https://www.choicehotels.com/CN761?mc=blypypaf', None, 'http://www.spayaz.com/locations/north-phoenix-az/', 'http://www.rollingartgroup.com', 'http://www.ymcacharlotte.org/saras', None, 'http://www.campwaggingtails.com', 'http://www.elwoodbodyworks.com/', 'http://www.abramseyeinstitute.com', 'http://jumbocrabchampaign.com', 'http://www.goldeneyecarelv.com', 'http://espressoamano.com/', 'http://www.francescaselyria.com', 'http://www.drirwinsimon.com', 'http://www.fullcirclepet.com/', None, 'http://designoneprinting.com', None, 'http://www.lowbooksaleslasvegas.com/', 'http://www.serviceking.com/locations/service-king-99th-ave?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://falconrelocation.com', 'http://www.bowtiepizza.com', None, 'http://www.quakersteakandlube.com/', '1592758597', 'http://locations.michaels.com/nv/henderson/2870/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.arbys.com', '1592758606', None, 'http://www.kiza.ca', 'http://www.animalcliniccalgary.com/', 'http://www.coldstonecreamery.com/stores/21109', None, 'http://www.lvperio.com/', 'http://www.clinicalafamilia.com', None, 'http://www.parivartanyoga.com', None, 'https://www.longhornsteakhouse.com/locations/mo/independence/independence/5142?cmpid=br:lh_ag:ie_ch:dry_ca:LHQ121LOCURL_dt:20200619_sn:yelp_gt:independence-mo-5142_pl:locurl_rd:1105', 'http://www.aarcs.ca', 'http://www.outerlayer.com', 'http://www.tritoncabinets.com', 'http://www.apartmentmoverohio.com', '1592758643', 'http://clickserve.dartsearch.net/link/click?lid=43700044280191558&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, None, 'http://www.johnsproclean.com', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.thehumanbean.com', None, None, 'https://prettygirllingo.com', None, 'http://www.savoryhill.com', 'http://www.t4upgh.com', None, 'https://www.northridgevilleflorist.com/?srccode=yelp_track', 'http://local.firestonecompleteautocare.com/north-carolina/charlotte/5340-e-independence-blvd/?lw_cmp=IYP_YPC_MLP_10790', None, None, None, 'http://flavorscharlotte.com', None, None, None, 'http://www.chardonvet.com/', 'http://www.coldstonecreamery.com/stores/20127', None, 'http://www.acehelpful.com', 'http://www.casadiamore.com/', 'http://www.deibertgrouplv.com', None, 'https://www.frysfood.com/storeHours?store=66000121', 'https://www.nodaselfstorage.com', None, 'http://www.torontohemp.com', 'http://www.lawans.com/', 'https://mattressmanphoenix.com', 'http://www.leeleesupermarket.com/', 'http://www.silo13.ca', 'http://truckmasters.com', 'http://www.econrads.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PITWI', 'http://www.partycity.com', 'http://www.mark-taylor.com/arizona/san-valiente/', 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.preferredfootankle.com', None, 'http://regalnailslasvegas.com/', 'http://www.greatclips.com/', 'http://www.pacificsales.com/', 'http://fixauto.com/allen-expressway', None, 'http://www.thespiritofcuba.net/', None, None, 'http://www.aliantegaming.com/spa/', 'http://www.crownpointresort.com', None, 'http://www.spiralvolleyball.com', 'http://www.kalamazoovaporshop.com/kzoovaporlyndhurstoh', 'http://www.madeleines.ca/', 'http://www.gameagainstores.com/', 'https://www1.shoppersdrugmart.ca', 'http://www.rabba.com/', 'http://www.artiumology.com', 'http://www.oneself-therapy.com', 'https://potslv.com', 'http://www.qwfootmassagespa.com', 'http://www.windwalkerexpeditions.com/', 'http://pitapit.ca/', None, None, 'https://www.jugojuice.com', None, 'http://www.edmarshalljewelers.com', 'http://franklygoodcoffee.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLTSH', 'http://www.maxhealthlv.com', None, '1592758831', 'https://www.francescas.com', 'http://www.magentahealth.ca', None, '1592758841', 'http://www.goldenruletattoo.com', None, '1592758848', None, 'http://www.starbucks.com/store/15623/', 'http://nijosushi.ca/', 'http://www.howardsjewelrycenter.com', 'http://pier88yachtclub.com', 'http://www.felixswimschools.com', 'https://gymvmt.com/clubs/macleod/', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.martinez-lawn-service.com', '1592758871', 'http://www.angelosmcfarland.com', 'https://www.trulynolen.com/location/arizona/sun-city-pest-control?utm_source=yelp&utm_medium=listing&utm_campaign=', None, 'http://www.trio-charlotte.com', '1592758883', 'https://hilalgrill.com', None, None, 'http://www.hydraulichoseassembly.net/hosepower/locations/arizona/mesa-arizona/', 'http://mjdphotography.co', 'http://www.landoncooling.com', None, 'http://suddenlyslimmer.com', None, 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'http://www.zipcar.ca/toronto', None, 'https://www.searchcontrol.com', 'http://www.ollies.us/locations/2308-matthews-township-pkwy-matthews-nc/', 'https://www.goldenstatestorage.com/self-storage/nv/henderson/golden-state-storage-horizon-ridge', 'https://www.gianttiger.com/store-locator/giant+tiger+%23159.do', None, 'http://hertz.com', 'http://pulselasvegas.com', '1592758921', None, None, 'http://www.dynamicgreens.com', None, 'http://www.aircityair.com', None, None, 'http://orderforbesgyros.com', 'http://www.theeyeplaceonline.com/', 'http://www.marshallsonline.com/tjx/directions.aspx?sid=121', 'http://motel6.com', 'http://www.dirtydogdepotsc.com', 'http://www.donbluthfrontrowtheatre.com', 'http://www.mtgcheese.com', 'https://us.megabus.com/?utm_source=Yelp&utm_medium=Yelp&utm_campaign=Madison%20Page', 'https://locations.riteaid.com/locations/pa/wexford/10554-perry-highway.html', 'http://www.annaspasalon.com', 'http://marybrowns.com', None, '1592758972', 'http://www.mulliganspub.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://thrifty.com/loc/ll/US/NV/LAS-VEGAS-AP/7135-GILESPIE-STREET', None, None, None, 'http://www.texturstudio.com', '1592758987', 'http://www.yveschantre.com', None, None, 'http://www.imperialdragonrestaurant.com', None, None, None, None, 'http://stylehouselasvegas.com', None, None, 'https://www.boulderbrewpub.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.tcmlawgroup.com', 'http://www.dollargeneral.com', None, 'http://www.randyscomputersllc.com', 'https://www.pizzahut.ca/store-details/store-R32814/pizza-hut-Mississauga', None, None, 'https://www.frysfood.com/storeHours?store=66000064', None, '1592759043', None, None, 'http://www.structube.com', 'https://indacocharlotte.com', 'http://www.evcds.com', None, 'http://www.arizona4x4offroadrecovery.com', None, 'http://www.celebritytanning.com', 'http://www.fitnesswithatwistpgh.com/', 'http://locations.harristeeter.com/nc/charlotte/205/', '1592759082', None, None, 'http://www.guitarriot.com', 'http://www.abodyinbalancelv.com', 'https://www.thegrovevegas.com', None, None, 'http://www.rosetuxedoaz.com', 'http://ads.yorkbbs.ca/zhnyg/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.yourinnervagabond.com', 'http://www.auntieannes.com/', 'http://www.tkservicecenter.com/', 'http://smartcleanerslv.com', None, None, None, None, None, 'https://casa-del-taco-mexican-restaurant.business.site', 'http://www.mattamyathleticcentre.ca', 'https://www.madisonboats.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.hudecdental.com', 'http://www.dranene.com', 'http://www.thehabanero.ca', 'https://www.bringfido.com/attraction/2775/', 'http://www.FootAnkleInstituteAZ.com', 'http://www.319coffee.com', '1592759191', 'http://www.arizonasportsclinic.com', None, 'http://carolinasportsmassage.com', None, 'http://www.wbrockcity.com', 'http://blomedry.com/locations/blo-blow-dry-bar-las-vegas-nevada/', '1592759213', 'http://www.daleadams.com/', 'http://cwanimalhospital.com', 'http://arizonaccc.com', 'https://www.cunninghammortgage.com/', None, 'http://www.waterstreetdistrict.com', None, None, None, 'http://www.thai-sa-on.com/', 'http://www.Tempourbanbistro.com', 'http://www.nachodaddy.com/henderson/', 'http://charlottepetvet.com', None, 'http://bomontipizza.com', None, 'https://www.capriottis.com', 'http://www.newgranadarestaurant.com', 'http://www.thefonestore.ca', 'http://animalhospitalofcornelius.com/', 'http://www.truehealthteam.com', None, None, 'http://www.azartsolutions.com', 'http://www.chinesedrs.com', 'http://www.AllergyForAll.com', None, 'http://cici-nail-studio.business.site', None, None, 'http://www.dancetotherhythm.ca', 'https://www.ushagent.com/dawnblack', 'http://www.samstownlv.com/dine/willy-and-joses-cantina', 'http://www.awcollision.com', None, 'https://chasefieldevents.com/stadium-venues/the-draft-room/', 'http://www.availvapor.com', 'http://www.willowroomsalon.com', 'http://www.westmarine.com/stores/phoenix-az-523', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://anevadaplumbing.com', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', None, 'http://www.sonicdrivein.com/', None, 'http://www.ritasice.com', 'https://www.mcalistersdeli.com/locations/nc/charlotte/9864-rea-road-suite-a-1237', 'https://www.chick-fil-a.com/scottsdale101', 'http://www.nettiesneatandtidy.com', None, None, 'https://www.arrowheaddentistry.com/?utm_source=VYRLYelp&utm_medium=CTA', 'http://www.garyfranzen.com/', 'http://www.massageforlifewaxhaw.com', 'http://www.samstownlv.com/dine/firelight-buffet?disid=wmm_yelp_st_corporate_firelight_organiclink', None, 'http://massageheights.ca/locations/Crowfoot.aspx', 'http://thedenhookah.com', 'http://www.americaneagleautoglass.com', 'http://showappeal.com/', None, None, 'http://www.desertbloom-mobilevet.com', 'https://www.sportchek.ca/stores/burloak.html', 'http://www.mrtilelv.com', None, 'http://www.littlelebanonpita.com', 'https://www.walmart.com/store/5497/evans-mills-ny/whats-new', None, 'http://www.thewaggingtaillv.com', 'http://hyatt.com/gallery/torphannon/', 'http://www.tacohausaz.com', None, None, '1592759459', 'http://www.amazingawardsaz.com', 'https://www.caesars.com/planet-hollywood?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=PlanetHollywood&utm_content=hotel', '1592759472', 'http://www.divanailsaz.com', 'http://miracleeyebrows.com/', 'http://www.orleanscasino.com/dine/alder-and-birch?disid=wmm_yelp_to_corporate_alderbirch_organiclink', 'http://www.genospizzaandmore.com', None, 'http://timtatman.com', 'http://www.arbys.com', 'http://dipyourridelv.com', 'http://www.dermace.ca', 'http://www.trufusionbluediamond.com', None, 'http://popeyeschicken.ca/', 'http://www.vitospizza.com', 'http://www.bowlasian.com', 'http://www.plumbing-excellence.com', None, 'http://www.instyprintschampaign.com', 'https://www.nsbank.com/branch/?branch=durango_and_215_south_branch', 'http://www.annamarisol.com', None, None, None, 'http://www.ilashscottsdale.com', 'http://www.mystellabellashop.com', 'https://www.artinstitutes.edu/las-vegas?source=YEXTY&school=AiLV&utm_medium=local&utm_source=Yext', None, 'http://www.shawarmakingaz.com/', 'http://www.hairbyjnicole.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89128/027192/', '1592759581', None, 'http://www.stillwaterspacalgary.com', None, None, None, 'https://michaelangelos.ca', None, 'https://www.circlek.com/store-locator/us/surprise/11339-w-bell-rd/2706285', 'http://www.evoswimschool.com', None, 'http://lvcabs.com', 'http://www.unclesamssubs.com/', 'https://www.azdivorceattorney.net', None, 'http://confined.ca', 'http://www.sportsmans.com', 'https://www.usps.com/', 'https://couturemedical.com', 'http://www.hightenedpath.com', 'http://www.toepel.com', 'http://www.readymixaz.com', None, 'http://www.bachiburger.com/', 'http://ftfinancialinc.com', 'http://www.uwcu.org', 'http://www.aamcopeoria-az.com', 'https://www.lindt.ca/en/stores/lindt-chocolate-shop-holt-renfrew-centre', None, 'https://www.grandandclover.com', 'https://als-gyros-chicagos-finest-greek-restaurant.business.site', None, 'http://www.dixieford.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.firehousepizza911.com', '1592759699', 'http://www.bluebrushes.com', None, None, None, 'https://www.atlanticaviation.com/location/LAS', 'http://massageheights.ca/locations/shepard-regional.aspx', None, 'http://www.flexed.com', 'http://www.delreycleaners.com', None, 'http://www.case.edu', 'http://phxdogs.com', 'http://www.waterfordatpeoria.com', None, 'http://adrianspizzaross.com', None, 'https://www.honorhealth.com/physicians/lori-travis', 'http://www.unisonbar.com', 'https://www.mastermechanic.ca/locations/home.php?location=BramptonHeartLake', 'http://fiveguys.com/', None, None, 'http://www.pinkabellacupcakes.com/surprise-az', 'http://www.avenuenissan.com', None, 'http://www.deltechservice.com', 'http://www.clmlocksmith.com', 'http://maisnailsandlash.com', None, None, 'https://comforcare.com/nevada/lasvegaswest', None, 'http://lasvegas.carenow.com/location/arby-durango', '1592759806', None, None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280216206&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', None, 'http://stores.barnesandnoble.com/store/2745', 'http://www.fancofans.com', None, 'http://www.bigboyswithcooltoys.ca/', 'https://www.olivegarden.com/locations/nv/las-vegas/las-vegas-cheyenne-ave/1363?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:las-vegas-nv-1363_pl:locurl_rd:1274', 'http://www.fosteranimalhospital.com', None, None, 'http://www.shaheenfoodcentre.com', 'http://www.allcreaturespetsitaz.com', 'http://backyarddreambuilders.com', None, 'https://www.aspendental.com/dentist/pa/pittsburgh/420-clairton-blvd?utm_source=yelp&utm_medium=lociqyext&utm_campaign=PleasantHills%2CPA%7C%7CPlsnHls_PA%7C%7C8134&utm_content=listing', 'http://www.mirsung.com', None, None, 'https://www.t-mobile.com/store-locator/az/scottsdale/scottsdale-fashion-sq-2?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.marbleslab.ca', 'http://littlelambcleaning.com', 'http://www.auntieannes.com', 'http://www.cpaexpress.biz', 'http://www.twiceisnicelv.com', 'http://www.nordkuste.com', None, 'http://www.foreveryoungsalon.ca', None, None, 'https://www.walgreens.com/locator/walgreens-2363+s+lindsay+rd-gilbert-az-85295/id=5215', None, 'http://www.smokespoutinerie.com', 'https://www.townestorage.com', 'http://www.caju.ca', 'http://www.milanomusic.com', 'http://www.mark-taylor.com/arizona/domus/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, None, 'http://autorelocationspc.com', None, 'https://www.metropcs.com', 'http://www.tidedrycleaners.com', 'https://www.mapleacura.com', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.scdentalgroup.com/home/sc-dentistry-at-palm-valley.aspx', 'http://www.designerfabrics.ca', 'https://locations.nekterjuicebar.com/ll/US/AZ/Chandler/7131-W_-Ray-Rd_*-Ste_-8?utm_source=yelp&utm_medium=link&utm_campaign=Casa-Paloma&utm_content=URL', 'http://www.kabutoindiangrill.com', None, 'http://getinfinitepotential.com', None, 'https://www.discounttire.com/store/oh/macedonia/s/1951?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://kidiatricdental.com', 'https://stores.mooresclothing.com/on/oakville/2501-hyde-park-gate.html?utm_source=yelp&utm_medium=listing&utm_content=97&utm_campaign=ON', None, 'http://cjautorepair.wix.com/lasvegas', None, 'https://www.prestigecleaners.com', None, 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', 'http://www.katuradayspa.com', 'http://indianflavour.ca', 'http://www.safeway.com', 'http://www.blackearthmeats.com', '1592760052', 'http://cruuncorked.com', 'http://www.mobiledentmedic.com', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.centralcoffeeco.com', 'http://bellanimalhospital.com/', 'http://www.za-pizzeria.com', 'http://www.capinaseatery.ca', 'http://www.offtheavenue.com', None, None, None, None, '1592760100', 'http://www.loyaltsalon.com', None, 'http://www.memphischampionshipbbq.com', 'http://www.mountainviewbeeremoval.com', None, 'http://www.imanishi.ca/', 'http://bakecode.com', 'http://www.perfectimagecenter.com', None, 'http://www.monkeybargym.com', 'http://hudecdental.com/office-locations/garfield-heights-oh', None, 'http://bloomdispensary.com', 'http://www.infinityfitnessaz.com', None, 'http://www.sandboxstudios.ca', None, 'https://experimac.com/summerlin-south-nv/?utm_campaign=yelp_ads&client=8014-80135&utm_medium=CPC&campid=20&utm_source=yelp', '1592760177', 'http://www.reedco.org', 'https://www.jiffylube.com/locations/az/phoenix/2098', None, None, None, 'http://www.thecollectivehairstudio.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://pranicjanelv.wixsite.com/pranicjanelv', None, 'http://www.theroy.ca', 'http://foodconnect.org/phxmarket/?page_id=8147', 'http://www.goldennugget.com/', 'http://www.unclealspizza.com', 'http://www.empireaccountants.com/', 'http://www.kaizenbeltsushi.com', 'http://www.brockstespresso.ca', None, '1592760237', 'http://www.avebusiness.com/', None, 'http://www.dairyqueen.com', 'http://www.allstaranimalhospital.com', 'http://www.tkcafes.com', None, None, 'http://www.mamastouchmassage.com', 'http://www.yollipop.net', 'http://mywakeuptomakeup.com', 'http://www.noahseventvenue.com', 'https://locations.monro.com/pa/wexford/10551-perry-hwy?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.independencemazda.com/', None, 'http://www.monettitailoring.com', 'http://www.gbyguess.com', None, 'http://jaguarslasvegas.com', 'http://cyclone-muaythai.com', 'https://www.vistas707.com/?utm_source=yelp', 'http://puresweatspa.com', 'http://www.dovecleaners.com', '1592760317', 'http://www.shutterscheap.com/', 'https://www.walgreens.com/locator/walgreens-1725+northport+dr-madison-wi-53704/id=2967', None, None, 'http://luv2play.com/rh/', 'http://www.applespice.com', 'http://www.pnc.com', None, 'http://www.eggsmart.ca', None, 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6081', None, 'http://grayhawkgolf.com/', 'http://www.charterfitness.com/locations/find-a-location/?address=61801&miles=50', 'http://www.mobisquad.com/', 'http://www.diamondjims4cash.com', None, 'http://www.quiktrip.com', 'http://www.sunchain.com', 'https://myhoneybakedstore.com/gastonia/1508', None, 'http://community54.com', None, 'http://www.liveatrubix.com', 'http://www.scottsdalelivestock.com/', 'http://www.posin.com', None, None, None, 'http://furegrace.wix.com/spa-olive', 'http://digitell.com', 'https://nathansfamous.com/restaurants/luxorhotelcasino-lasvegas-130416/', None, 'http://www.rumbi.com/las_vegas.php', 'https://partyplanetsuperstore.com', 'https://www.regmovies.com/theatres/regal-great-northern-mall-rpx-ohio/1773?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Great+Northern+Mall+&+RPX+-+Ohio', None, 'http://www.coachscornergrill.com', None, 'http://www.akpblinds.com', 'http://travelingcaddy.com', None, None, 'http://laserspa.vegas', 'https://www.torrid.com/store-details?StoreID=5664', None, 'http://hybridfitness.org/', 'http://www.cluberoticapittsburgh.com/', 'http://charlotte49ers.com', 'https://www.myphoenixdoctor.com', 'https://www.moneytreeinc.com/branch/north-nellis', None, 'http://www.kenzington.ca', 'https://cordesperformanceracing.com', None, 'https://dermahealthinstitute.com', 'http://www.patcatans.com/craft-store-locations/bedford-oh', None, 'http://www.burritobandidos.com/', None, 'https://sites.google.com/site/joskarenjones/', 'http://www.indianhut.ca/', None, 'https://www.heinens.com/Heinens-of-Rocky-River', 'https://calibercollision.com/locate-a-caliber-collision-center/charlotte-tyvola-rd', 'http://www.hcxcharlotte.com/carmel-commons-hair-salon/', 'https://altaviapgh.com', 'http://www.julescafe.ca/', None, 'http://www.calciumbegone.com', 'http://www.burgerking.ca', None, 'http://www.greatclips.com', '1592760560', 'https://www.alexandermd.com', 'http://www.rosedaleclub.com', None, 'http://www.wliaz.com', 'http://www.Diablos.biz/', None, 'https://www.cartridgeworld.com/las-vegas-nv/89102-0318/about-us', 'http://www.avalon.edu/locations/mesa-az/', '1592760596', 'http://pachucagrill.com/', 'http://www.marcos.com/locations/nc/charlotte/s-tryon-st--suite120', 'https://www.mydrnow.com', None, 'http://www.pepperandcompany.net', 'http://www.azatss.com/', 'https://www.chronicinktattoo.com/locations/tattoo-shop/chronic-ink-midtown-toronto-yonge-eglinton/', 'http://citizensbank.com/', 'http://www.southeastharley.com', 'http://www.RefreshSkinCare.com', 'http://www.avondaletoyota.com', None, None, None, 'http://www.arizona-homeinspection.com', None, 'https://www.phoenixsigncompany.org', 'http://www.depryacupuncture.com', 'https://www.suncityendo.com', 'http://www.sfpetclinic.com', 'http://www.brookstoneapartments.com', None, None, 'http://www.mtplumbinglv.com', None, 'http://www.upmc.com', 'http://www.madisonsales.net', None, 'https://www.terrysautodetailingcoraopolis.com', 'http://arrowsecurityinc.com', None, 'http://wiseacresorganic.com', None, 'http://boomerangsresale.org', 'http://www.theupsstorelocal.com/0832', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://www.warhol.org/visit/', 'https://placebell.ca', 'https://www.reigntoronto.ca', 'http://www.labranche.ca', 'http://phoenixmountainah.com', '1592760748', 'https://www.painclinic-lv.com', None, 'https://www.discounttire.com/store/nv/henderson/s/1300?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.quesada.ca', 'http://www.costco.com/warehouse-locations/avondale-az-691.html', 'http://www.amatokingpizza.com', 'http://deforestvision.com', 'http://www.expressionsbridalformal.com', 'http://www.nuzzlers.net', 'http://www.umacleveland.org/', None, 'http://www.vinniezucchini.com', 'http://www.maccosmetics.com', 'http://www.lakewoodhardware.com', None, 'http://www.kustomkolorsllc.com', None, 'http://www.simply-wellness.com', 'https://www.lasvegasnvdentist.com', None, 'https://www.bannerhealth.com/locations', None, None, 'http://www.cassandraclinic.com', 'http://georgebarbersalon.com/', None, 'http://www.pizzahut.com/', None, 'http://www.stevenmarzullolaw.com', 'http://www.kimnailsspa.ca', '1592760851', 'https://waisalterations.business.site', 'http://doubletree3.hilton.com/en/hotels/pennsylvania/doubletree-by-hilton-hotel-pittsburgh-airport-PITARDT/index.html?SEO_id=YELP-DT-PITARDT', 'http://apstraining.com', 'https://www.csn.edu/vets-center', None, 'http://www.oakmonttavern.com/', 'https://toddsprivatecarserviceandamazingtours.com/local-trips/', 'https://www.chapmanchryslerjeep.com', 'http://www.shinytime.ca', 'http://www.coldnosecompanions.com', 'http://www.golfsmith.com', None, None, 'http://eglintoncarpets.com/', 'http://www.otoh.ca', 'http://SourceAcademyELC.com', '1592760914', None, 'https://locator.chase.com/oh/beachwood/22801-chagrin-blvd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.deandeluca.com/', 'http://pizza.dominos.ca/Oakridges-Ontario-10448', None, 'http://www.kitchenstuffplus.com', 'https://www.andrewspartyrental.com', 'http://www.currynmorenc.com', None, 'http://www.ernstlanes.com', 'http://keepnitgreenlv.com', None, 'http://www.leveluplv.com', None, None, None, None, 'http://hodgeshappycleaners.com', 'http://www.pcsavants.com', 'http://www.wendys.com', '1592760982', 'http://www.tnt-supermarket.com', None, 'http://www.dominos.com', None, None, None, 'http://www.superiortire.ca/locations/mode/10/5070-sheppard-avenue-east-scarborough-on-m1s4n3.aspx', 'http://www.philipdudalaw.com', 'http://www.fivelampschophouse.ca', None, None, '1592761021', 'http://magiconeauto.com', 'http://www.healthfare.ca', None, 'http://www.arborpointelv.com/', 'http://airtechautomotive.com', 'http://www.cocoaberry.ca', 'https://thepetclub.com', 'http://www.eighteeneight.com/avon-oh', 'http://www.dianaxu.com?cmpid=tb5b_blm_0006', 'https://stores.madewell.com/en/scottsdale-fashion-square?srccode=X%7CPMG%7CNaturalSearch%7CLocal%7CYelp%7C239', 'http://www.thedemicup.com', '1592761060', 'http://www.tacobell.com', None, None, None, 'http://www.exceptionalcareforanimals.com/', 'https://sonaskin.com/location-results/charlotte-midtown/', '1592761084', 'https://local.firestonecompleteautocare.com/arizona/phoenix/1141-e-bell-rd', None, '1592761095', None, '1592761103', 'http://www.flightcleveland.com', 'http://www.ntb.com/store/8481/waxhaw-nc-28173-9046?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'https://www.brakesplus.com', 'http://www.calgaryclimbing.com/locations/stronghold', 'https://www.firstam.com/title/nv/las-vegas/?utm_source=yelp&utm_medium=organic&utm_campaign=residential-local-search&utm_content=nevada-las-vegas', 'http://barre3.com/studio-locations/torontoksw', 'http://www.bankofamerica.com', 'http://www.bigawoodfiredpizzeriaoh.com', 'http://www.aaronsplumbing.ca', 'https://www.sslexus.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://www.bashas.com/Locations.aspx?city=Apache+Junction', 'https://www.craigscookies.com', 'http://www.quiktrip.com/', 'http://www.ruffinitresort.com/?utm_source=yelp&utm_medium=social', 'http://99only.com/store/Mesa---Main/', 'https://www.planetfitness.com/gyms/surprise-az?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, None, 'http://www.dominos.com', None, 'http://www.brothersfurniture.ca', None, 'http://performtolearn.com', 'http://www.excalibur.com/amenities/pool.aspx', 'http://www.cheesecakeandcrime.com', None, None, 'http://www.paradisespa.ca', None, None, 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.letutor.com', None, 'https://haircutmenmckeefarmsmatthewsnc.com', 'http://www.arbys.com', 'http://nestlecafe.com', 'http://garganos-catering.com/index.html', None, None, 'http://www.prestigepetsalon.net/', 'http://www.beautifulmedspa.com', 'https://www.urbanoutfitters.com/stores/crocker-park-oh', '1592761249', None, 'http://seasonalsurvivalhvac.com', 'http://www.dollarama.com', '1592761263', 'http://dannystruckwash.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.kurevapes.com', 'http://www.jennyspopcorn.com', 'http://thesidekickcomics.com', None, 'http://www.harkinstheatres.com', None, 'http://www.clearchoicemechanical.com/', None, None, 'http://www.wfsandwiches.com', None, None, None, None, None, 'http://www.barrontattoo.com', 'https://bcautomotivellc.com', 'http://www.modelmilk.ca', 'http://urbannorthinns.com', 'http://www.azroyalgranite.com', None, None, None, 'https://www.loblaws.ca/store-locator/Loblaws+-+St.+Clair+Ave+West/1212?storeId=1212', 'https://www.calgaryzoo.com', None, 'http://speedylocksmithphoenix.com', '1592761357', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.henrys.com/stores/3-Mississauga-Heartland.aspx', 'http://www.sunsetstation.com', 'http://www.happyharvestersaz.com', None, 'http://lorikarl.com', 'https://keithclinic.com/locations/north-charlotte/', 'http://tremontathletic.com', None, 'http://www.y1now.com', 'http://www.camelbackconsignanddesign.com', 'http://firstchoice.com/salondetail/default.asp?salonid=5068', 'https://www.petsmart.com/stores/us/wi/madison-store0604.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.rondopools.com', 'http://www.azclinicalservices.com', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'https://www.flyfrontier.com', 'http://www.quiznos.com', None, None, 'http://www.dennystv.com', 'http://www.petinthecitync.com', 'http://www.remnantministries.net', None, 'http://www.therustyrudder.net', 'http://pattystamales.net', 'http://bodybykotoske.com', None, 'http://www.harveys.ca', 'http://insaneairaz.com/', None, None, None, None, 'http://www.mailshoppeaz.com', '1592761472', 'http://www.richmonddentalclinic.com', None, 'https://www.applebees.com/en/restaurants-cleveland-oh/3401-steelyard-drive-76017', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.banfield.com/veterinarians/az/tempe/tmp?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, 'http://azfamilypaint.com', 'http://www.shell.us', 'https://7leavescafe.com', 'https://locations.sonicdrivein.com/nc/concord/296-highway-29-north.html', 'http://www.theprintingspot.ca', 'http://knifewear.com/', None, 'http://www.bigmouthmarketing.co', 'https://www.homesteadins.com', 'http://energyonewater.com', None, None, 'http://precision-autobody.com', None, 'http://www.galleriasm.com/branch/store/ov', 'http://www.symposion.ca/', 'http://www.divinecharter.com', None, 'http://www.jimshorkeychryslerdodgejeepram.com', 'http://www.verizonwireless.com/stores/ohio/mayfield-heights/mayfield-201974/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', 'http://www.shaunaspawspa.com', 'http://www.budgetlasvegas.com/locations', None, 'https://www.bannerhealth.com/services/academic-medicine/banner-university-medicine-institutes/banner-university-medicine-heart-institute', None, 'https://www.qltyshoerepair.com', 'https://www.bestdentalcarelv.com', None, 'https://www.redroof.com/property/AZ/Tempe/RRI265', 'http://aclimateresponse.com/', 'http://radicalroadbrew.com', 'http://www.arbys.com/', 'http://www.filibertos.com/', 'http://www.matthewsfootcare.com/', None, 'http://www.shopjustice.com', 'https://directvdealer.com/arizona/mesa/first-choice-communications?CID=DTV:AFF:YLP:LBM:yelp:yelp:yelp&utm_source=affiliate&utm_medium=referral&utm_campaign=yelp', 'https://locations.waxcenter.com/pa/murrysville/murrysville-0487.html', 'http://www.yummysaz.com/', None, 'http://www.sushitoki.ca', 'http://www.beyondbedtimebooks.com', 'https://www.caferio.com/locations/eastern', None, '1592762158', 'https://easymovers.com?utm_source=yelp', 'http://www.secondcup.com', 'http://www.thelittleclinic.com', '1592762171', 'http://roomescapeadventures.com', 'https://vantagewest.org', 'http://www.stonewallnursery.com', 'http://www.altvatersautosales.com', None, 'http://www.twallenterprises.com/watermark-lofts/', 'http://www.drterkonda.com', 'http://www.oceanne.net', None, None, 'https://www.bluestonetherapyaz.com', 'http://www.surgical-dermatology.com/victoria-farley-md/', 'http://gelato64.com/', None, 'http://www.zoomrentals.com/calgary-airport-car-rentals', 'https://locator.chase.com/az/avondale/1545-n-dysart-rd?jp_cmp=rb/LocalListings/aff/branch/na', '1592762229', None, 'http://www.euclidlibrary.org', 'http://vitapath.ca', None, 'https://order.subway.com/Default.aspx', 'http://www.gridirne.com/', 'http://www.chandleroms.com', 'http://www.heroburgers.com', 'http://www.7-eleven.com/?yelp=22886', None, 'http://www.highrollertransportation.com', 'http://rocker7farmpatch.com', None, 'http://thetoastedtangerine.com/', 'http://www.arizonamaintenanceservice.com/', None, 'https://www.liveatsunstone.com/?utm_medium=Listing&utm_source=Yelp', 'http://www.silverspurtours.com/', 'http://barrett-jackson.com/', 'http://www.gastonpourhouse.com', None, 'http://www.grandpearl.ca', None, 'http://www.aprilspetcare.com', 'http://japan-49.com', 'http://kebobchi.com/', 'http://iblowdry.com', 'http://www.richtree.ca', 'http://www.sandmanhotels.com/hotel/quebec/montreal', 'http://www.668euclidave.com', None, 'http://thesingingmechanic.com', 'https://www.bannerhealth.com/locations/phoenix/banner-university-medical-center-phoenix', 'http://www.sarecycling.com/?utm_source=Yelp%20Website', None, None, 'http://benjisgrill.com/', 'http://www.phxevolution.com/', 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', 'http://www.mountainviewoptometry.com/locations/mountain-view-optometry-crowfoot', 'http://www.mycountryclubsmiles.com/', 'http://www.lifetimeheart.com', '1592762371', None, 'http://www.perfectthreading.com', 'https://www.spoonerpt.com/locations/avondale/', None, None, 'http://www.scottsdaleweightloss.com/', None, 'http://www.microsoft.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://integritycarpetandflooringservices.com', '1592762408', 'http://www.newbeginningsobg.com/', None, 'http://www.shell.com', 'http://www.JimmyJohns.com', 'http://www.strosenh.org/locations/sahara/', None, None, None, None, None, 'http://www.visionsource-laveen.com', 'http://www.pizzamilano.net/', None, None, 'http://ubburger.com', 'http://tikiz.com/SEValleyAZ', 'http://www.phoenixcarpetandupholstery.com/', 'http://sauerbrothers.com', 'http://www.iheartwaffles.net', 'https://stores.bestbuy.com/oh/macedonia/470-e-aurora-rd-758.html/?loc=ns100&ref=NS', None, None, 'http://www.contemporarycraft.org', '1592762481', None, 'https://friocreamery.business.site', 'https://www.canyonpeds.com', 'http://www.cluttermenotjunkremoval.com', 'http://www.marriott.com/hotels/hotel-information/restaurant/cltbr-renaissance-charlotte-suites-hotel/', None, 'http://www.almeidaroofing.com', 'http://www.sensake.com', 'http://altercareonline.com/', 'http://www.mentor-ridge.net/default.aspx', None, 'http://seasonsgourmetcatering.com/', 'https://www.bedroomstoday.com', 'http://www.secondcup.com/location/toronto-355-danforth-avenue', 'http://clickserve.dartsearch.net/link/click?lid=43700044282975385&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.gatewaycc.edu/trade-technical-training-programs', None, 'http://www.ottopizza.com', 'http://www.nevadasafes.com', 'http://www.gianteagle.com/Stores/Store/?storeId=70', 'https://desertforesthairdesign.glossgenius.com', None, 'http://www.potbelly.com/Camelback?utm_source=ExtNet&utm_medium=organic&utm_campaign=Yext', 'https://locations.nekterjuicebar.com/ll/US/AZ/Scottsdale/6137-North-Scottsdale-Rd*-Ste_-105?utm_source=yelp&utm_medium=link&utm_campaign=Hilton-Village&utm_content=URL', 'http://www.rabys.ca', 'http://www.majestybakeries.com', 'http://perrytownedrafthouse.com', '1592762560', 'http://www.oasisanimalclinic.com/', None, 'https://www.choicesaz.com', 'https://extremepita.com', 'http://thfashions.org', 'http://www.larrydjinis.com', 'http://randdmotors.com', 'http://bellanottescottsdale.com/', None, None, None, None, 'http://www.portcredit.com', None, None, None, '1592762597', None, '1592762600', 'http://www.dicksbicyclerepairshop.com', 'https://megafurnitureusa.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3210+East+Union+Hills+Corner+Of+32nd+Street-Phoenix-AZ-85050/storeid=3264?cid=ps_ylp_2020', None, 'http://hkm.com/lasvegas', 'https://www.nationalflooringlv.com', 'http://www.powerhour360.com', '1592762620', None, 'http://www.desertstorage.com/peoria-az-self-storage', 'https://www.sawstarsmaltesepuppys.com', None, None, 'http://www.italianvillagepizza.com/', 'http://www.mobilityunlimited.ca/', 'http://www.fcbanking.com', 'http://www.pueblomedicalimaging.com', None, None, 'http://www.ourcare.com', 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', '1592762654', None, 'http://www.cbsa-asfc.gc.ca/prog/nexus/application-demande-eng.html', None, None, 'http://eathealthyeatgreek.com/locations/tempe-mill-avenue/', 'http://www.ALegUp.ca', 'http://www.cocokaramel.ca', 'http://sharewineloungeandbistromonroeville.gastro-america.com', None, None, None, 'https://www.thaibythepark.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://kaardbombe.com/', None, 'http://vegasdaylandscape.com', 'https://spartamovers.com', 'http://www.7-eleven.com/?yelp=35581', 'http://www.baseelectronics.ca', None, None, None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'https://www.napaonline.com', 'https://www.hcafecanada.com', 'http://www.chinainn.info', 'http://www.vapers.ca', 'http://www.mysisterscloset.com', None, None, None, None, 'http://xoliquorlasvegas.com', 'http://towne380.com/?lang=fr', None, 'http://www.thed.com/dining/', 'http://www.momentsfound.com', 'http://www.jusfruit.ca', None, 'http://www.treehousecleveland.com', 'https://bhmanagement.com/communities/nc/charlotte/runaway-bay-apartments-1299', 'https://www.mckenzietownebarbershop.com', None, 'https://www.focuseventphotography.com', 'http://www.shopmodernique.com', 'https://www.cabinetcoatings.com', 'http://www.drshachinapalace.com', 'http://www.tiptopstow.com', 'http://www.belleetboeuf.com/anjou/', 'https://www.summerlinhospital.com/?utm_medium=referral&utm_source=yelp', 'https://thrivemed.com', 'http://www.mizusushiparma.com', None, None, 'http://www.mrfreshbarbershop.com', 'http://www.hunterortho.com', 'https://www.thejoint.com/wisconsin/madison/gammon-watts-30004', 'http://www.pickeringappliances.ca', 'http://markhamgaragedoors.com', 'http://disappearinginkltr.com', None, 'http://www.allamericanfire.com', None, 'http://www.vivalasvapor.com', None, 'http://www.racewaycarwash.com', None, 'http://www.juliesclothing.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.journeys.com', 'https://www.jasonsdeli.com/restaurants/metrocenter-mall-deli', 'http://www.myjoesdeli.com', 'http://www.pghfilmmakers.org/exhibition/showtimes.html', None, None, 'http://www.papabubbleto.com', 'http://www.creativesalonandspa.com', None, None, None, None, 'http://www.marcos.com/', 'http://www.novaklaserboutique.com', '1592762866', 'http://popeyes.com', 'http://www.thekitchentable.ca/bathrst.html', '1592762873', None, None, 'http://www.a1photo.ca', '1592762884', 'http://www.shrine-circus.com/', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.villagejuicery.com/', 'http://www.centrainternalmedicine.com', 'http://www.hairremovalbyelectrolysis.ca', 'http://www.rockyriverdental.com/', None, None, 'http://www.kaowheels.com', 'http://www.quiktrip.com', 'https://www.firstcalgary.com/locations/village-square', None, 'https://www.finfeatherfur.com/locations/middleburg-heights.html', 'http://www.tuxone.com', None, 'https://www.astainedglassweddingchapelvegas.com', 'https://www.siennaliving.ca/long-term-care/locations/St-George.aspx', '1592762949', 'http://kb-confections.com', 'http://www.JimmyJohns.com', 'http://revsolve.com/', 'http://www.mysuncreek.com', 'http://www.usps.com', None, 'http://Www.YourNevadaLender.com', 'http://fiveguys.com/', 'http://www.cuadventures.com', None, 'https://www.benjerry.com/miraclemile', None, 'http://inti-restaurant.com', 'https://local.firestonecompleteautocare.com/nevada/las-vegas/3770-s-maryland-parkway/', 'http://www.shagovac.com/', None, 'http://www.thedrakehotel.ca', 'http://educosalon.com', 'http://www.roastcoffeeandtea.ca', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4402+Oakhurst+Boulevard-Harrisburg-PA-17110/storeid=1641?cid=ps_ylp_2020', None, 'http://www.azadifinerugs.com/locations/scottsdale/', None, None, 'https://carrellchiropractic.com', 'http://www.bubblesnbakery.com', 'https://www.purespeedracing.com/', None, 'https://www.cricketwireless.com', 'http://www.blueicelounge.com', 'http://www.rusticsourdoughbakery.com', None, 'https://www.unioncornersbrewery.com', 'http://academymortgage.com/jakekrabbe', 'https://www.clubpilates.com/springvalley/', 'http://www.imagineexhibitions.com/VENUES/ImagineExhibitionsGallery/tabid/451/Default.aspx', 'http://www.mrhero.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___northwest', 'http://www.gragolawncare.com/', 'http://thebeautyloungetoronto.com/', 'http://www.thewineshoponbay.com', None, None, 'http://www.gabesstores.com', 'http://www.cicis.com/locations/nv-las-vegas-9890-s-maryland-pkwy', None, 'http://www.facesmd.ca', None, None, None, None, 'http://www.cruiseamerica.com/rv-rental-locations/rv-rentals-charlotte/', None, 'http://www.brandcastle.com', 'http://baileysoutdooradventures.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1111+North+Dunlap+St-Savoy-IL-61874/storeid=5887?cid=ps_ylp_2020', 'http://www.biggranch.com', 'https://integrityautoservicemadison.com', 'http://parkavenueblowdry.com', None, None, 'https://www.panerabread.com/en-us/home.html', 'http://www.midas.com/cleveland/store.aspx?shopnum=4234&dmanum=212', 'http://www.midwaychevrolet.com', None, 'http://www.americancaninetraining.com', None, 'http://www.tropicalsmoothiecafe.com', 'http://www.worldmarket.com', None, None, 'https://www.caesars.com/harrahs-las-vegas/shows/big-elvis', None, 'http://www.teddycastro.com', '1592763214', 'http://www.jennsmassageheaven.com', 'http://leathermangolf.com/', 'http://www.vivaeltacoexpress.com', None, 'http://www.prayosha.ca', 'http://www.rvrepair2u.com', None, 'http://www.asiancafepittsburgh.com', None, 'http://www.friendlydentalrivergate.com', 'https://www.frysfood.com/storeHours?store=66000627', 'https://www.perfecthairandmakeup.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.narcisselounge.com', None, None, 'http://www.decidedlyjazz.com', 'https://locations.postnet.com/az/chandler/2925-e-riggs-rd', 'http://www.waggintailspetinnandsalon.com', None, 'https://www.phoenix.gov/parks/sports/complexes/reach-11', 'http://www.ohiopestpro.com', 'http://www.achemicalromancesalon.com', 'http://www.soldbythelynchs.com', 'http://www.backyardconnect.com', 'http://www.zoyogurt.com/frozen-yogurt-in-paradise-valley-scottsdale/', 'https://www.alfaromeoofscottsdale.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://www.RockbarScottsdale.com', 'http://www.starbucks.com/store/9334/', 'http://www.cityofhenderson.com', None, None, 'http://www.amanospizza.weebly.com', 'https://paris-paris-wine.myshopify.com', 'http://www.bjnoodlehouse.weebly.com', None, 'http://www.mccarran.com', 'http://janinebeautycare.com', 'http://www.chandlerhandlers.com/', None, 'http://www.sizemattersrentals.com', None, 'https://www.supercuts.com/locations/az/gilbert/frys-shopping-center-haircuts-82716.html', 'http://nutritionfixaz.business.site', None, None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTCW', None, 'http://www.lcbo.com', 'https://www.hbtbank.com/locations/urbana-il-philo-road', None, None, 'http://www.timbersgaming.com', 'https://locations.panerabread.com/oh/broadview-heights/2000-e-edgerton-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', None, None, 'http://www.bsalonbar.com', 'http://www.brooklyncaferestaurant.com/home.html', 'https://petesgrill.business.site', None, 'http://www.cprtentandevents.com', 'https://azsenate.gov', None, 'http://www.aznypdpizza.com', 'https://www.greekpalace.net', 'http://funhousejumpers.com/', 'http://www.luxurysuitesintl.com', 'https://thefosterfarm.wordpress.com', 'https://tommys-express.com/LasVegasNV15?utm_source=ExtNet&utm_medium=Yext', '1592763479', None, 'http://www.hottiehair.com/', 'https://www.promechautomotive.com', None, 'http://www.missinglinksausage.com/', None, None, 'http://www.canopi.com', None, 'http://www.barhopbar.com', 'http://www.heartprintsmontessori.com', 'http://www.calgaryfitbodybootcamp.ca', 'http://www.greatcooks.ca', None, 'https://www.shamrockbowlandrestobar.com', None, 'http://www.timhortons.com', 'http://www.mtroyal.ca', 'http://www.goosecreekautomotive.com', 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'http://www.azautorv.com', '1592763551', 'http://www.arco.com', 'https://www.thedinnerdetective.com/cleveland/tickets-showtimes/#buyTixDates', 'http://www.thomasderm.com', 'http://www.strongfabriccare.com/', None, 'https://palmbeachtan.com/locations/AZ/Scottsdale-North-Via-Paseo-Del-Sur/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'http://www.dignitymemorial.com/mariposa-gardens-memorial-park/en-us/index.page', 'http://www.signaturemgmgrand.com/restaurants/thelounge.aspx', 'http://bigegg2009.com', None, 'http://thornleamedicalcentre.com', None, None, 'http://www.burlingtoncoatfactory.com', 'http://jenniferpilates.com', None, 'http://kunaheating.com', 'https://www.trueresults.com/phoenix-az', '1592763615', 'http://showmars.com/locations/gastonia-321', 'http://espressoamano.com/', 'http://freddysusa.com/', 'https://www.olivegarden.com/locations/oh/middleburg-heights/middleburg-heights/1073?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:middleburg-heights-oh-1073_pl:locurl_rd:1042', 'http://charlottecafeinc.com', 'http://www.advantagenv.com', 'http://walmart-eyedocs-lasvegas.com/Marks-Sunset', None, 'http://www.motortech.us/', '1592763651', None, 'http://www.southmaincycles.com/', None, 'http://www.dunwellz.com/', 'http://www.lillyrocket.com', None, None, 'http://www.westernfarmpc.com/', None, 'https://ziva-nail-bar-at-scottsdale-waterfront.business.site', None, 'http://mcmurdielaw.com', 'http://www.detat.com', 'https://www.bacaropizzeria.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://my.clevelandclinic.org/locations/directions/240-sports-health-center', 'http://www.superior-tire.com', None, 'http://churrasqueiraestrela.com', None, 'http://www.mirvish.com/theatres/edmirvishtheatre', None, None, 'http://www.oreillyauto.com', 'https://www.theshadestore.com/showrooms/north-carolina/charlotte?utm_source=yelp&utm_medium=cpc', None, 'https://www.samstownlv.com/casino-gaming/bingo', 'https://deltabingo.com/our-locations/st-clair/jackpots', None, 'http://www.timhortons.com/', 'http://www.dennys.com', 'https://wolfgangpuck.com/dining/spago-lv/?utm_campaign=spago-lv&utm_medium=las-vegas&utm_source=yelp-listing', None, 'http://www.quantobasta.ca/', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'https://www.lewisapartments.com/sahara-west-las-vegas-nv/?utm_campaign=yelp&utm_source=yelp&utm_medium=paid&utm_content=yelp-page-sw', 'http://www.bmwmoc.com/', 'http://www.mountainparkplumbing.com/', 'https://cocofreshtea.ca', None, None, None, 'http://www.broadwaycheesecakeco.com/', None, None, None, None, 'https://ad.doubleclick.net/ddm/clk/458671617;262921492;r', None, 'http://www.mayura.ca', None, 'https://www.sushiaoi-yonge.com', 'https://www.rootcauseresolution.life', 'http://www.allamericanoutdoorliving.com/chandler-location', None, 'http://doria.ca', 'http://sukhaspa.ca/', 'https://www.wellsfargo.com', 'https://www.tlcbarandgrill.com', 'https://www.chilis.com', 'https://www.hungryhowies.com/store/hungry-howies-00908?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00908&utm_content=Website_Link', None, 'http://www.kellyandsonsauto.com', None, 'https://www.cobsbread.com/local-bakery/applewood-plaza-mississauga/', 'https://www.pizzahut.ca/#!/store-details/store-R30902/Richmond%20Hill', None, 'http://www.americawest.com', 'https://gunselmans.com', '1592763883', 'https://www.gerbercollision.com/locations/tempe-priest-dr-az', 'http://www.chateauamore.com', 'http://www.dominicandesignsalon.com', 'https://mandarinrestaurant.com/brampton/', None, 'http://bradley-stone.com', 'http://www.penn-station.com', 'http://scottsdaleskinbar.com', None, 'http://portofinowest.com', 'http://www.giveshelter.org/', None, 'https://phoenixiphonerepairmasters.business.site', 'http://storelocator.pepboys.com/pepboys/stores/bethel_park/bethel_park/00371', 'http://www.ConsueloSouders.com', None, 'http://thecarpetconnectioninc.com/', 'https://www.maplehonda.com', 'http://www.pvrugs.com', 'http://www.starbucks.com/store/15757/', '1592763956', None, 'http://www.keepsaketrophy.com', 'http://www.simoncarter.ca', None, None, 'http://www.jokerstattoobodypiercing.com', 'https://www.lindt.ca/en/stores/lindt-chocolate-shop-holt-renfrew-centre', 'http://www.theaceofservice.com', 'http://www.jimmyssimplygoodfood.com/', 'http://www.northvalleysmiles.com', 'http://www.kefferjeep.com', None, None, 'http://www.tastecosupermarket.com', 'https://www.goodcaraz.com', None, None, 'http://www.sanplumbingsupply.com', None, 'http://www.cernyshoes.com', '1592764033', None, 'http://www.drcarriehui.com', 'http://www.phoenixusedcarsaz.com/', None, 'http://mamareneesrestaurant.com', 'https://www.usps.com/', 'http://www.desertvisioneyecare.com/', 'https://www.t-mobile.com/store-locator/az/peoria/67th-peoria?cmpid=WTR_SE_YXT_U98MLWB9027148', 'https://locations.massageenvy.com/arizona/goodyear/1468-n-litchfield-rd.html', 'http://www.ulyannachung.com?cmpid=NYYE_BLM_0006', 'http://www.paylesscar.com/locations/phoenix-phx/', '1592764074', 'https://marinonassif.com', 'http://kumaris.ca', 'http://www.acquadolcetoronto.com', 'http://www.restaurantmonvillage.com/contact.htm', None, 'https://www.sweye.com/locations/scottsdale-bell-rd/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-scottsdalenorth&utm_content=website', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.protagonistbeer.com', 'http://mesatvappliance.com', 'https://www.dairyqueen.com/ca-fr/Locator/Detail/?store-id=2028&localechange=1', 'https://acuityeyecenter.net/Location.html', 'http://www.rocknes.com', 'http://www.ourladyofsorrows.org/', 'http://www.lolasfilipinokitchen.com', None, None, 'http://www.marshallsonline.com/store-finder/204', 'https://www.goodfellasbarberaz.com', 'http://locations.traderjoes.com/nc/charlotte/742/', 'http://www.onenevada.org', 'http://www.pittsburghclo.org', 'https://cycletiquepgh.com', 'http://www.fqstory.org', 'http://www.rossstores.com', 'http://mascuisine.com/', 'http://www.starbucks.com', 'http://www.cloudninespa.com', 'http://www.albertahealthservices.ca', 'http://skatelandsavoy.com', 'http://primus.ca/', 'https://www.greasemonkeyauto.com/peoria-illinois-61614-center-177', 'http://www.imageautobody.ca', None, None, 'http://www.starbucks.com/store/9298/', None, None, 'http://www.conns.com/store-locator/arizona/mesa-85204', 'http://www.bodyheattanning.com', 'http://www.cervantesgaragedoor.com', 'http://www.georgeschophouse.net/', 'http://www.itskarate.com', 'https://www.petsuppliesplus.com/Store/NC/Charlotte/Charlotte/8052?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'http://www.phxortho.com', 'http://www.parisenvy.com', 'http://www.bistro36.ca', '1592764242', '1592764245', None, None, 'http://www.mycarolinababy.com', None, 'http://tokyodiscountvegas.com', None, 'https://www.smolictire.com', None, None, 'http://Herballygrounded.com', 'http://www.steelcitybeer.com', 'http://www.amcheck-lasvegas.com', None, 'http://wedionphoto.com', 'https://local.fedex.com/oh/beachwood/office-1231/', None, 'http://www.mychickenshack.com', 'https://www.truedentistry.com', None, None, 'http://www.timewarpbar.com/', 'http://www.idealcoffee.ca', 'https://www.ffl.net/locations/lakewood-branch', 'https://southbeachtanningcompany.com/unc-charlotte/', 'http://www.thepowerofyourawareness.com', None, 'http://provider.kareo.com/dr-mark-burdorf', None, 'http://www.upymca.org', 'http://www.tuthillflowers.com', 'http://www.sentry.com', 'http://www.thelashattic.com', 'http://www.goldenjoyrestaurant.com', 'http://www.edwardsanddavies.com', 'http://reallycleanphoenix.com/', 'http://www.snapfanatic.com', 'http://lveyebrowthreading.com', 'http://www.protospace.ca/', None, None, '1592764372', 'http://www.AZmoves.com/Dane.McFall', '1592764379', 'http://www.connectionsacademy.com/arizona', 'https://southlakedentistry.com', 'http://www.thebuildingcenterinc.com', '1592764395', 'http://skfence.com', 'http://samsxpresscarwash.com/university', None, 'http://www.thehickorytavern.com/home/hickory_tavern-locations.php?l=Charlotte+-+Providence+Rd.', None, 'http://eosfitness.com/location/ahwatukee?utm_campaign=ahwatukee&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', 'http://www.septicpumpingservicenc.com', 'http://bk.com/', 'http://waterboypoolservice.com/', None, None, 'http://www.emergencychiropractic.com/our_locations/scottsdale', None, None, 'https://www.flyfrontier.com', '1592764451', None, 'http://www.trevi-restobar.com', None, 'http://smergliachiropractic.com', 'http://www.ouzeri.com/', 'https://stores.hallmark.com/pa/westmifflin/amys-hallmark-shop-westmifflin-pa-40670.html', 'http://shellrapidlubeservice.com', 'https://www.twilightcafe.ca', 'http://www.florenciapizzabistro.com/', None, None, 'http://www.racewaycarwash.com', 'http://www.onekingwest.com/hotel/dining/', 'https://www.restoamir.com', 'http://cave-creek.certapro.com//?source=Yelp', None, None, None, 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.mafiamikespizza.com/', 'http://freshco.com/stores/steeles-bathurst/', 'https://www.dunnedwards.com/directory/store-list/surprise-140', 'http://www.dreamworxink.com', None, None, 'http://www.helixtransportation.com', 'https://www.xfinity.com/local/pa/pittsburgh/5211-brownsville-road.html', '1592764542', 'http://www.sbbqc.com', None, 'https://www.searchsolutiongroup.com', 'http://www.buttercreambakeshoppe.com', None, 'https://www.wellsfargo.com', 'http://www.patthairestaurantlasvegas.com/', 'http://www.marriott.com/hotels/travel/pitbr-renaissance-pittsburgh-hotel', None, 'http://www.aquatouch.com', 'http://exchangetowertradesecrets.simplybook.me/sheduler/manage', 'https://www.heritage-communities.com/senior-living/az/surprise/orchard-pointe-surprise/', None, 'http://www.waterwingsswimschool.com', 'http://www.thingsremembered.com', 'http://www.spilsburyorthodontics.com', 'http://www.mollybrownsswimwear.com', 'http://www.penn-station.com/', 'http://jerusalemcafematthews.com', None, 'http://www.cometvet.com', None, 'http://www.labcorp.com', 'https://www.tgifridays.com/locations/1852/fridays-las-vegas-west-nevada', 'http://www.negativespacecleveland.com', 'http://www.tagteamsigns.com', 'https://movemycar.us', 'https://cashtime.com/loan-center-details/1133-w.-broadway-rd-mesa-az-85210', '1592764640', 'http://www.clethestandard.com', None, 'http://chocolate-emporium.com', 'http://www.tmtgolf.com', 'http://www.markville.ca/en/Pages/default.aspx', 'http://www.wil-mar.org/reserve-a-room', 'http://www.serenitymassageandwellness.ca/', None, 'http://newimagelasvegas.com', None, 'https://www.bannerhealth.com/locations/sun-city/banner-olive-branch-senior-center', None, None, 'http://www.lifebaptistchurch.com', 'http://GoSolarLasVegas.com/offers', 'http://thevaultwhitby.com', None, 'http://www.swisswatchery.ca', 'http://www.bon-appetit.ca/', None, 'http://www.deseretmarketinggroup.com', 'https://www.oneazcu.com/about/locations/phoenix-monroe-st/', 'http://www.wolfgangpuck.com/', None, None, None, 'https://slotburger.com', 'http://eluxattramonto.com/?utm_medium=listing&utm_source=Yelp', None, 'https://www.simon.com/mall/summit-mall', 'http://www.syntheticgrassstore.com/Home', None, None, None, None, None, None, 'http://fastenerslv.com/', 'http://www.pearlwest.com/', 'http://www.roseandsons.ca', 'http://queennailsetobicoke.ca', 'http://www.tinaalexandertileanddesign.com', 'http://MWE@extendedstay.com', 'http://www.visionsource-rhodesranch.com', 'https://bbqmexicana.com', None, 'https://agents.allstate.com/the-taylor-family-agency-las-vegas-nv.html', 'http://www.superstarcarwashaz.com', 'http://ovenandvine.com', None, 'http://www.presotea-ab.ca', 'http://www.aulitfinelinens.com', 'http://www.phx360fitness.com', None, 'http://manhattanpizzaiilv.com', None, 'http://www.usapurebredlabs.com/', 'http://www.azjetski.com', None, 'http://www.verradogolfclub.com/verrado-grille/', None, 'http://www.crowncovervpark.com', None, None, 'https://www.davidsbridal.com/?utm_source=Yelp&utm_medium=OrganicSearch&utm_term=208&utm_content=DisplayURL&utm_campaign=WebsiteListing', 'https://child-care-preschool.brighthorizons.com/NC/Charlotte/carillon', None, 'http://www.jesseherfel.com/', 'http://progressiveagent.com', 'http://nappys.ca', 'http://www.muriettaapartments.com', 'https://sunsetspasaz.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.precisionfit.net', 'http://www.littlecaesars.com', 'http://spartanarms.vegas/', None, 'https://hisworkmanshiplabor.com/cities/madison-wisconsin/', 'http://www.illustrioushardwoods.com', None, 'http://www.theepittsagain.com', None, 'http://www.abcstores.com', 'http://www.victoriousflooring.com', 'http://www.azlifetime.com', 'http://thecorallife.com', 'https://www.naumannhobbs.com/locations/arizona/phoenix/', None, None, None, None, 'https://www.chronicinktattoo.com', 'http://www.dapreschool.com', 'http://www.raydiancesuntanstudio.com', 'http://www.choicepoolcare.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.chicos.com/store/home.jsp?cmp=MOC_yelp', 'http://www.executivelasvegas.com', None, 'https://www.prestigecleaners.com', 'http://www.redbullairrace.com', 'http://spinettisgaming.com/', 'https://www.modernacupuncture.com/arizona/phoenix/arcadia-az011', '1592764976', 'http://5anddiner.com/', None, 'http://www.boxlunch.com/stores-details?StoreID=4588', 'http://centerforadd-az.com/', 'http://www.summerlink.com/recreation-and-parks/parks-and-amenities/parks#pueblo', None, None, 'http://www.ilthy.com', None, 'http://www.doitallplumbing.com', 'https://risasdental.com/find-a-location/oral-surgeon/?utm_campaign=LocationPage&utm_medium=OralSurgeonYelpWebsite&utm_source=Yelp', 'https://www.sprint.com/locations/oh/parma-heights/6341-pearl-rd', '1592765017', 'http://www.nellosscottsdale.com/', 'http://www.studiobdental.com', None, None, 'http://www.tsh.to', None, 'http://www.tivolivillagelv.com/', 'http://www.frysfood.com/', None, 'http://blomedry.com/locations/blo-bloor-west-village/', 'http://www.animalmedical.net', 'http://www.ripepi.com', 'http://www.lexusofchandler.com', 'https://www.bobevans.com/our-restaurants/locations/186?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://checkmateshoes.com', 'http://www.spoiledbaby.info', 'https://www.teachershealthtrust.org', 'https://www.roosterboycafe.com', None, None, 'http://shell.com/', None, 'http://www.fletcherstireandauto.net/', 'http://www.spearmintrhinolv.com/', 'http://www.rougeboeuf.com/', 'http://www.uhhospitals.org/macdonald', None, 'http://www.marshallsonline.com', 'http://clubfortunecasino.com/dining/', None, 'https://firstnailz.com', 'http://www.scottsdaleaz.gov/fire/fire-stations/station-11', '1592765117', 'http://www.kegsteakhouse.com/en/locations/ON/scarborough/estate-drive-keg/', 'http://www.2ndswing.com', 'http://info.lululemon.com/stores/us/glendale/westgate-outlets', 'http://www.tri-chiro.com', 'https://www.thewildfloweraz.com', None, None, 'https://www.cleurbanwinery.com', None, 'http://www.cocellipizza-yonge.ca', 'http://www.mannacafe.com', 'http://www.gianteagle.com/Stores/Store/?storeId=0229', 'https://www.youfit.com/gym/phoenix-32nd-st-7406', 'http://www.panonthedanforth.com', 'http://waxhawfarmersmarket.org', 'http://www.dressforsuccess.org/affiliate.aspx?sisid=131&pageid=1', 'http://www.nmdiner.com', 'http://samirhairdesign.com/', 'https://www.dimsumkingrestaurant.com', 'http://www.geneslocksmith.com', 'http://www.aladdinseatery.com', 'http://goldenhandschinesebodywork.com', '1592765193', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.fabulouseyebrowthreading.com', 'http://www.simply-cinema.com', 'https://locations.churchs.com/az-phoenix-7235', 'http://www.shreddinglv.com', 'http://www.leandersbarbershop.com', 'https://www.cwsapartments.com/marquis-of-carmel-valley-charlotte-nc/', 'https://www.dickeys.com', None, None, '1592765232', None, None, 'https://www.starbucks.ca', None, 'http://freshwheelsaz.com', 'http://www.bradfordendo.com', 'http://peacegardenchildcare.com/', 'http://www.studio89.org/', None, None, None, 'https://www.pier1.ca', 'http://www.frabonisdeli.com', None, 'http://vintagepoolslv.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.clechiropractic.com/', None, 'http://toiledclovertattooparlor.myonlineappointment.com', 'http://www.funhogranchlv.com', None, 'http://www.metal-galaxy.com', 'http://www.sonathreading.com', 'https://local.fedex.com/nv/las-vegas/office-1441/', None, 'http://www.drstoneaz.com', None, 'http://www.puppiesnlove.com', 'http://www.comfortcravingsaz.com', None, 'http://www.revfittherapy.com', 'http://www.wellsfargo.com', 'https://www.burger21.com/locations/charlotte-ballantyne/', 'http://www.aquilis.com/', None, 'http://www.metro-hardwoods.com/', 'https://www.circlek.com/store-locator/us/peoria/9476-w-olive-ave/2706468', 'http://rocketfizz.com/locations/rocket-fizz-charlotte-nc/', None, 'https://www.target.com/sl/las-vegas-blue-diamond/2164', 'https://www.hansonsoutfitters.com', None, None, 'https://www.hyperionworks.com/business/', 'http://www.superliquorvegas.com', 'http://www.edc03.com', 'http://www.restaurantmonza.com', 'http://florasalon.ca', None, None, 'http://www.scoopydooconcierge.com', 'http://tcby.com/', 'http://www.rmsaquaculture.com', 'http://www.ethelschocolate.com', 'http://www.bridgewatercapital.com', None, 'http://www.supeckseptic.com', None, 'http://childrensplace.com/', 'http://www.theclarkbar.com/', 'https://nationwidevision.com/locations', 'http://12westbrewing.com', 'http://www.francisandsonscarwash.com/category/7871/francis-and-sons-car-wash-of-glendale-az.htm', 'http://www.friendscafe.ca/location.html', 'http://www.mavisroadanimal.ca', None, None, 'https://www.zenmassageusa.com/Huntersville/', 'http://www.novotel.com/gb/hotel-0841-novotel-toronto-mississauga-centre/index.shtml', 'https://www.obhhospital.com/?utm_source=Yext&utm_medium=organic&utm_campaign=listing&utm_term=brand', 'http://www.charlottecarpetguy.com', 'http://www.vocellipizza.com/', '1592765493', 'http://www.vcahospitals.com/black-mountain/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Black_Mountain_Animal_Hospital&utm_campaign=main_url', None, 'http://www.subway.ca', None, None, 'https://stores.advanceautoparts.com/nc/charlotte/2910-freedom-drive?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', 'http://cinemark.com/theatre-1144', 'http://www.cookiesbygeorge.com', 'http://www.togos.com', 'http://www.designersfurniturecleveland.com', 'http://momoplace.business.site', 'http://www.dreamhomefunder.com', None, '1592765544', 'http://www.spicehouse.ca', 'http://www.dundeesdeliandbar.com/', 'http://www.oakcraft.com/', 'http://autoservicemallinc.com', 'http://www.livingstreams.org', 'http://www.misssixty.com', 'http://www.bloomingdalelimousine.com', None, None, 'http://westcoastmotorsaz.v12soft.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://www.spadaforas.net', None, 'http://www.one10pgh.com', None, 'http://www.foodiescateringaz.com', 'http://wojtilasbakery.com', 'http://www.goodstuffusa.com', 'http://nnelegant.ca', '1592765614', 'https://stores.toysrus.com/nv/lasvegas/toy-store-las-vegas-nv-5607.html', 'http://www.beadsnbotanicals.com', 'http://www.7-eleven.com/?yelp=29384', 'http://evo-massage.com', None, None, 'http://www.kaboom.com/Ontario-Etobicoke-Albion.html?utm_source=yelp', 'http://www.jacobi702.com', 'http://www.sandsglendale.com', None, None, 'http://www.uwcu.org/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.arizonagolfresort.com', 'https://www.carefreesmilesdentistryaz.com', 'http://www.hollywooddiamond.ca', None, 'http://www.smlsolutions.ca', 'http://www.thedancingdandelion.com', 'http://www.fadefactoryclt.com', 'http://www.litespressobar.com', 'https://www.fredastaire.com/phoenix-central', 'http://www.topdoglv.com', 'https://www.gowireless.com/stores/co/glendale/glendale-colorado-blvd/', 'http://www.starbucks.com/store/11665/', 'https://www.eliteigroup.com', 'https://www.purebarre.com/location/toronto-queen-st-west-on', 'http://www.strikerssoccer.com', None, 'http://www.nicolestoverhair.com', 'https://www.lebos.com', 'http://www.bk.com', 'http://www.dolcewraps.com', 'http://www.vocellipizza.com/scotttownship_pa', None, None, 'https://www.ooliortho.com', None, 'http://www.uhhospitals.org/concord/urgent-care', 'http://www.arahovasouvlaki.com', None, 'http://www.phxpoolpros.com', 'https://anahairdesign.com', None, 'http://pittsburghwindowblindscompany.com', 'http://www.hkcenters.com/', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2faz%2fphoenix%2fscottsdale-north&sisearchengine=1524&siproduct=2637_Bus', '1592776621', 'https://www.tidedrycleanersaz.com/locations/e-frank-lloyd-wright-blvd', 'http://www.starbucks.com', None, None, None, None, 'http://www.littlegreenplanet.ca', 'http://etobicoke.handymanconnection.com', None, 'https://www.neosmedspa.com', 'https://www.beckygarcia.com', 'http://www.sonicdrivein.com', None, None, 'http://maxvelocityPT.com', 'https://www.urbanboba.com', 'http://www.crabcornerlv.com/', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.casablanca212.com', 'http://www.andysdeadbug.com', 'http://costcutters.com/salondetail/default.asp?salonid=62072', 'http://www.lapizzsuperchoix.com', None, 'http://calgary.smartypantz.ca/?ref=calgary', 'https://www.southstburger.com/location/3021-argentia-rd/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.thewildvineuncorked.com', 'http://fairwaysatcavecreekliving.com', None, 'http://justaddwaterstreet.com', 'http://www.highwayautocenter.com/', 'http://www.goodwillaz.org/location/goodwill-mckellips-mesa/', 'http://www.buabuathai.com', 'http://www.scrapbookersparadise.com', 'http://www.eliteglassandmirror.com', None, None, 'http://www.folinobrothers.com', 'https://www.180smoke.ca/vape-store-scarborough-180-smoke-electronic-cigarettes-e-juice-vaporizers', None, 'http://www.madisondentalcentre.com', 'http://www.thecal.com/dine/redwood-steakhouse?disid=wmm_yelp_ca_corporate_redwoodsteakhouse_organiclink', 'https://scarborough.weedman.com', 'http://www.makemydayflowers.com', 'https://www.girltribeco.com', 'http://ntnl.ca/national-17th/home-ntnl17', 'http://www.lowes.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://therockincrawfish.com/#!/lasvegas', '1592776805', 'http://www.sntfun.com', None, 'https://www.smartconnectlv.com', 'http://www.itsagrind.com/', 'http://www.richstowing.net', None, 'http://www.dunkindonuts.com', None, 'https://the-roti-spot.business.site', None, None, 'https://premierkitchenandbath.com', '1592776850', None, 'http://www.universitysuburban.com', 'http://www.personaledge.com/en/accueil.php', None, 'http://www.dalilah.ca', 'http://buttoutecigs.com', 'http://rosatisfrozencustard.com/', 'http://www.loveandsandwiches.com', '1592776883', 'https://www.moneytreeinc.com/branch/henderson', 'http://www.oakcrestpetcrematory.com', 'http://www.ci.middleton.wi.us/index.aspx?nid=175', 'http://www.casadelrioaz.com', 'http://www.alyssacampbellphotography.com', 'http://vbarbershop.com/locations/arcadia-phoenix/', None, 'http://angelicaholistic.com', 'http://www.clevelandairport.com/parking-transportation/parking', None, '1592776921', 'http://www.gnc.com', None, 'https://www.batteriesplus.com/store-locator/pa/pittsburgh/batteries-plus-186?utm_source=yelp&utm_medium=local&storecode=186', None, 'http://www.dollartree.com', 'http://www.lindaskitcheninc.com/', 'http://www.360thriftstores.com', None, None, 'http://zukos-pizza.com', 'http://charmeck.org/mecklenburg/county/ParkandRec/Parks/ParkPlanning/Pages/FirstWard.aspx', None, 'http://meatandfish.com', None, 'http://www.vivianshyu.com', '1592776973', None, 'http://www.korqwinehouse.ca', None, 'https://www.mdg.ca', 'http://www.gameonlakewood.com/', 'http://www.benmoss.com/', 'http://liveatnantucketcove.com', 'http://cell-doc.com/locations/tech-repair-charlotte-nc/', 'http://officialsecuritylv.com/', 'http://centreforadvancedskinrepair.com/', 'http://sassynailavondale.com', None, None, None, 'https://locations.wendys.com/united-states/oh/maple-heights/5360-warrensville-center-road', 'http://www.dottys.com', 'http://www.lasvegasweddingchapelpackages.com', None, 'http://www.bambooscottsdale.com/', 'http://www.nickysthaikitchen.com', 'http://Www.lashandlaser.com', None, 'https://www.walmart.com/store/5281/woodbridge-nj/whats-new', 'http://www.kickasana.org', None, 'http://www.pastafreshvegas.com', 'http://www.sweetwatersystems.com', None, 'http://www.joshsandbergmyopractics.com', 'https://rxioptical.com', None, None, None, 'http://www.vikaspa.com', 'http://www.mjssteelcity.com', None, 'https://kellytorres.com', 'https://www.chandlerwestauto.com', 'https://www.sushitaxi.net/fr/succursales/laval', 'http://www.extravaganzaevents.com/depotinfo.htm', 'http://www.totalwine.com/store-info/arizona-gilbert/1005', 'http://www.rmhofcharlotte.org', None, 'http://www.akautoshop.com/', None, 'http://ups.com', 'http://www.lashspastudio.com/our-locations/location-mcmurray-location', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://rocketfizz.com/locations/rocket-fizz-gilbert-az/', 'http://www.DrReeferalz.com', 'http://www.scottsdalerecovery.com/', '1592777118', None, 'http://www.quiktrip.com', None, None, 'https://www.independenceharley.com', None, None, None, None, 'https://www.lifestorage.com/storage-units/north-carolina/charlotte/28105/372-in-matthews/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NC-372&utm_content=website-link&howheard=IYE', None, None, 'http://www.taekwondobbw.com', None, 'http://kunafas.com', 'https://www.walgreens.com/locator/walgreens-1902+w+franklin+blvd-gastonia-nc-28052/id=5877', 'http://www.doublepizza.ca', 'http://www.subzeroaz.com', 'http://www.hashhouseagogo.com/', 'https://www.massageaddict.ca/newmarket/', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Glendale-AZ-85308/858061/', None, 'http://www.bikeauthority.com/', 'https://krannertcenter.com', None, 'http://thepizzacompany.biz', None, 'https://eternal-art-tattoo-parlor.business.site', 'https://www.officedepot.com', None, None, 'https://www.anytimefitness.com/gyms/690/Fitchburg-WI-53719/?utm_source=yelp&utm_medium=local', None, None, 'http://www.clemetparks.com', None, 'http://www.gamestop.com', '1592777204', None, None, 'http://www.franklloydwright.org', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'https://myhoneybakedstore.com/RockHill/1543', None, 'http://www.realestateprosaz.com', 'http://www.murrayhillmarket.net/', None, 'http://www.abogadoray.com', 'http://www.cozmodiva.com', 'http://www.marshallscanada.ca/fr/directions.aspx?sid=722', 'http://www.yongestreetphysio.ca', None, 'http://mtcharlestonresort.com', 'http://smutsbros.com', 'http://www.carolinakinderdevelopment.com', 'http://www.bigbitez.com/', '1592777257', 'http://www.sammyshawarma.com/', None, 'https://www.capitalchev.ca', 'http://fiveguys.com', '1592777271', 'http://www.mimosarestaurant.ca', 'https://www.aldoshoes.com', 'http://greatercharlotteoralsurgery.com', None, None, 'http://www.dollargeneral.com', 'http://www.markville.ca/en/Pages/default.aspx', 'http://www.visions.ca', 'https://www.35thavesewandvac.com', 'https://www.digitalartsolutions.com', None, 'http://www.wokthisway.ca', 'https://local.biglots.com/nv/north-las-vegas/4516?zcp=pd_local_yelp', None, None, 'http://NaturesOasisStores.com', 'http://www.jukeboxbandstand.com/', None, 'http://BluenileToronto.com', None, 'http://www.azdot.gov/mvd/hours-and-locations?utm_content=Callout&utm_medium=Website&utm_source=azgovHome&utm_campaign=HoursandLocations', None, None, 'https://www.sennecoglass.com', 'https://www.nike.com/retail/s/nike-las-vegas', 'http://www.acusports.ca', 'https://www.houseofhunanmiddleburg.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sweetpeppersdeli.com/', 'https://azcoppercanyon.com', 'http://www.dancedocs.com', 'http://www.thumbsupaz.com', 'http://www.lvcc420.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://southpointebottledepot.com', 'http://www.club1pittsburgh.com/', 'https://www.culliganlasvegas.com/locations/las-vegas-nv/970', 'http://www.mrhero.com', None, None, None, None, 'http://www.foodbasics.ca', 'https://www.alohayogaandhula.com', None, None, 'https://abortionclinicsarizona.com', '1592777394', 'https://www.cosmopolitanlasvegas.com/identity/offer/mischief-ahead?utm_source=yelp&utm_medium=organic&utm_campaign=yelp', None, 'http://www.fivestareconomy.com', 'http://www.kingcoffeeaz.com', None, None, 'http://www.allfamilycarepc.com', '1592777418', 'http://www.cykl.ca/', '1592777426', None, 'http://www.burrachos.com', 'https://www.msrenewal.com', None, None, 'http://www.edelweisscheeseshop.com', 'https://www.freewayinsurance.com/office-locator/freeway-insurance-phoenix-az-85028/', 'http://www.bk.com', 'https://massagelux.com/yelp-massage-2-chandler/', 'http://www.vidogisalon.com/', 'http://www.canyonfalls.com', 'http://cityofmentor.com/play/explore/garfieldpark/', None, 'http://fiveguys.com/', None, 'http://www.optiko.ca', 'http://www.zetianlimousine.com', 'http://www.medmo.org', 'http://5starnutritionusa.com/5-star-nutrition-champaign/', 'https://stores.mooresclothing.com/on/mississauga/5885-rodeo-drive.html?utm_source=yelp&utm_medium=listing&utm_content=69&utm_campaign=ON', 'http://almservices.construction', None, None, 'http://www.windowsontheriver.com', 'http://www.phoenixmobileautorepair.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.aamcokentoh.com', 'http://www.cadillacbar.com', None, 'http://www.metroplatingaz.com', None, None, None, 'https://www.rlgrill.com', 'http://Moonriverthaibistro1.com', '1592777561', 'http://www.sportsandfitnessexchange.com', 'http://shopforflowers.ca', 'http://www.2hippiesgnarlyburger.com', None, 'http://mettlertherapy.com', None, 'http://www.aesthetictherapieslaserclinic.ca', '1592777590', None, 'http://www.taproyal.com', 'http://www.mastrionis.com/', 'http://www.lingeriesuperstores.com/', 'http://stonepeppers.com', None, None, 'http://www.radatattattoo.com', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=6121&localechange=1', 'https://www.valleyhospital.net/?utm_medium=referral&utm_source=yelp', None, 'http://www.audimidtowntoronto.com', 'http://www.cityofeuclid.com/recreation/Parks', None, None, 'http://www.westvalleyent.com/', 'https://www.kungfuteatoronto.com', 'https://sweettomatoes.com/locations/nv/henderson-68/', 'http://www.villageinnrestaurants.com', '1592777664', None, 'https://www.bradfordfamilydentist.ca', None, 'http://moorepools.com', 'http://www.motorfabrik.ca', 'http://www.lasvegasfloraldesigns.com', None, None, None, None, 'http://www.clevelandmoto.com', '1592777700', '1592777704', 'http://www.superhome.biz', None, 'http://www.scarboroughanimalhospital.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, 'http://homewoodsuites3.hilton.com/en/hotels/ontario/homewood-suites-by-hilton-toronto-oakville-YYZOVHW/index.html?SEO_id=YELP-HW-YYZOVHW', None, None, None, 'https://www.unityphx.org', 'http://www.kimswings.com', 'http://www.twistedmotionlv.com', '1592777749', None, None, 'http://www.geaugaparkdistrict.org/parks/rookery.shtml', None, 'http://www.fixmyazac.com', 'http://www.thekwikcarwash.com', 'http://www.fidelity.com', None, 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'https://alterations-express.com/find-us/?store_id=1', 'http://www.packageplusprinting.com', None, 'http://www.chevys.com', 'https://www.alert360.com/locations/best-home-security-systems-phoenix/', 'http://www.dairyqueen.com/', None, None, None, 'http://www.localtavern.ca', None, 'http://heartlakemassagetherapy.com', None, 'https://www.alapts.com/apartments/nc/charlotte/ascend-at-1801/', 'http://www.osiskitchen.com/', 'http://splashnshinecarwash.com', 'http://www.tgifridays.com/', None, None, 'http://www.madfreshkitchen.com', None, 'http://www.protowingaz.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://clevelandcinemas.com/location/9159/Southside-Works-Cinema-Showtimes', None, None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'https://bookersbbq.com', None, None, None, 'http://www.jayneebellsalon.com', None, None, 'http://www.portraitinnovations.com/', 'http://www.maplebanquet.com/', 'https://www.santancv.com', 'http://www.vibrantskinbar.com', 'http://www.crowfootalteration.com', None, 'http://www.starbucks.com/store/9229/', 'http://www.pearlexpressrestaurant.moonfruit.com/', None, None, 'http://akashaart.com/', '1592777941', 'https://www.wilhelmautomotive.com/locations/arcadia/', 'http://www.hwarogroup.com', 'http://www.nectardesserts.com/', None, 'http://www.bigmammashouse.ca', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___dobson_village_ii', 'http://bleubarnbistro.com', 'http://californiasandwichesnorth.com', None, 'http://www.smileorthodonticsaz.com', None, 'https://stores.arhaus.com/oh/lyndhurst/24613-cedar-road.html', 'http://www.modernmodular.com', '1592777997', 'http://www.shopcleansource.com/', None, '1592778010', '1592778014', None, 'http://www.kwss.org', 'http://www.thankucoffee.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YULWH', None, 'http://echokaraoke.ca', 'http://thedailydetails.com', 'http://www.eco-tint.com', 'http://www.OmniaMcClintockByAvanti.com?utm_campaign=gmbclickthru&utm_medium=gmb&utm_source=google', 'http://www.oldnavy.com', 'https://poolmechanics.wordpress.com', 'https://www.patsdrycleanersaz.com/pinnacle-peak-pima-road/', 'http://colourgenics.com/', 'http://www.visitpittsburgh.com/about-pittsburgh/neighborhoods/strip-district/', 'https://www.anytimefitness.com/gyms/288/Las-Vegas-NV-89139/?utm_source=yelp&utm_medium=local', 'https://asmcmd.com/team/amon-t-ferry-md/', 'http://www.capriottis.com/', 'http://www.elitedentistrycenter.com', '1592778089', None, None, 'http://www.sweetbeadslv.com', 'http://arizonastonegallery.com', None, 'http://www.primarisconstruction.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://endlesscreationssalon.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://www.hitzfitness.com', None, 'http://www.myridgegateapartments.com', None, 'https://psychicanita.com', None, None, 'http://surfsettoronto.com', None, None, None, 'http://www.denimandsmith.com', 'https://www.intownsuites.com/extended-stay-locations/arizona/phoenix/west-2/', None, 'http://www.boosterjuice.com', 'http://www.sears.com', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.crosslandstudios.com%2fproperty%2fCrossland-Economy-Studios-Phoenix-West-hotel.html&sisearchengine=1018&siproduct=2613_Bus', 'http://www.iloristyle.com', 'http://www.clevelandlighting.com', 'http://www.oaklandfordlincoln.ca', None, 'http://www.cobblestoneautospa.com', 'http://accountinghelper.org/', 'http://www.gracerobinson.net?cmpid=B175_BLM_0006', 'http://www.10tation.com/', 'http://dubinabrewing.com', 'https://oceanpokeco.com', None, 'https://www.smithsfoodanddrug.com/storeHours?store=70600381', 'http://junkedfoodco.com/', 'http://www.ultimatecarpetcleaning.org/', None, None, 'http://freshandeasy.com/', 'http://www.stevoautoclinic.ca', None, 'https://bostonpizza.com/en/locations/newmarket.html', 'http://www.fourseasons.com/scottsdale/dining/crescent_moon/', None, 'http://www.starbucks.com/store/8167/', 'https://vbarbershop.com/location/chandler-fulton-ranch/', None, 'http://www.torontobrewing.ca', 'http://www.jestersmexicangrill.com', 'https://agents.allstate.com/roger-bentley-mesa-az.html', 'http://www.dynamicnursing.com', 'http://www.kepnerstavern.com', None, 'http://www.dingdoctoraz.com/', 'http://www.lasvegaslaundryservices.com', 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', 'http://www.sugarblossomsalon.com/', 'https://www.walmart.com/store/3733/tega-cay-sc/whats-new', 'http://www.swisschalet.com', 'http://www.bbquesgrill.com', None, '1592778322', 'http://www.starbucks.com/store/11823/', 'https://www.thejoint.com/pennsylvania/pittsburgh/mccandless-crossing-20001', 'https://locations.tgifridays.com/nv/henderson/4330-e-sunset-rd.html', 'http://thedrunkmunk.com', '1592778343', 'https://www.cratersandfreighters.com/custom-crating-solutions-y/?utm_source=Yelp&utm_medium=organic&utm_campaign=website_click', None, None, 'http://www.repo-zone.com', 'http://www.fumccharlotte.org', 'http://www.eastvalleycomputers.net', 'https://www.vitechmechanical.com', 'https://ad.doubleclick.net/ddm/clk/434415706;236814625;g', 'http://bareescentuals.com/on/demandware.store/Sites-BareEscentuals-Site/default/Home-Show?brandId=BM&cm_mmc=Yelp_-_Campaign_1', 'http://www.atlwingsyourway.com', None, None, 'http://elcatrin.ca', None, None, None, 'http://ambiancechocolat.ca', 'http://www.seasidemexico.com/', None, 'http://davidsonfarmersmarket.org', 'http://www.dansdoorrepair.com', 'https://albertahomeservices.com', 'https://druryhotels.com/locations/charlotte-nc/drury-inn-and-suites-charlotte-arrowood', '1592778429', 'https://www.get-go.com/Store/OH/Mentor/Mentor%20GetGo/3638', 'http://www.bubblebattlesaz.com', 'http://www.boraboratanning.com', 'http://www.KleinPickle.com', None, 'https://www.jerseymikes.com/8002', 'https://www.famousfootwear.com/?partnerid=YELP', 'http://www.advanceddentistry.com', 'http://www.metrolinaeye.com', 'http://www.whrc-wi.org/polloinka/', None, 'http://www.hardinacupuncture.com', 'http://undefeated.com', 'http://www.deansautorepairinc.com/', None, 'http://acupuncture-lasvegas.com', 'http://www.timewarnercable.com', None, 'http://lizandlottie.ca', 'http://www.slicespizzajoint.com', 'http://kefalosandassociates.com', None, '1592778506', None, 'http://www.kabukirestaurants.com/', 'https://detailorientedariz.wixsite.com/mysite', 'http://browlounge.com/lake-norman-location/', 'https://www.walmart.com/store/1464/charlotte-nc/whats-new', 'http://www.psglv.com', 'https://www.marieantoinettevegas.com', '1592778533', None, None, 'http://www.angiessoulcafe.com/locations.php', 'http://edibleartclt.com/', 'http://www.aspirebodycontouring.com', 'https://www.tophat-pro.com', None, 'http://theponyexpresscafe.com', None, 'http://kupfertandkim.com/', 'http://dddiscountmotorcycles.com', 'http://richtreenaturalmarket.com', None, 'http://www.7-eleven.com/?yelp=36154', 'https://www.halecoffee.com', 'http://www.SalonAzulAz.com', 'http://discount-drugmart.com/', 'http://www.HealthyOutlookFamilyMedicine.com', '1592778599', 'https://grill-n-chop.business.site', None, 'https://www.signaturestyle.com/locations/oh/eastlake/cost-cutters-vine-street-plaza-haircuts-15732.html', None, None, 'http://www.clubcycleonline.com', None, 'http://www.salsarito.com', 'http://www.cmu.edu/piper/stories/2016/october/dining-delivers.html', None, None, 'http://www.newhappynailslv.com', 'http://www.starbucks.com/store/9298/', 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', None, 'http://www.peachesthetics.com', None, 'http://www.mendocino.ca', None, 'https://www1.shoppersdrugmart.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.johnofalltradesaz.com', 'http://www.kaizen-sushi.com/', 'https://www.advancenv.com/contact/sandhill-e-flamingo/', 'https://leboudoirstudio.com', 'https://www.sephora.com/happening/stores/markham', None, None, 'https://www.skyharbor.com/PHXSkyTrain', 'http://www.longos.com/store/storedetails.aspx?store_no=5', None, None, 'https://locations.churchs.com/az-phoenix-7235', '1592778714', 'http://www.mrosmow.com', 'http://www.skinsavvyqueensway.ca', 'https://www.kohls.com/stores/az/chandler-619.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', None, None, None, 'http://www.cluckncup.com', None, 'http://www.broadstonegilbertheritage.com', None, None, 'http://www.helpinghandselectric.com', None, '1592778765', 'https://www.rolostore.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=2137&localechange=1', None, 'http://hermesbakery.com/', 'https://www.cellphonerepair.com/charlotte-myers-park-nc/', 'https://www.kimphat.com/en/store/67780/kim-phat-a-brossard', None, None, 'http://fashionliquidationoutlet.com', 'http://smiledirectclub.com', None, 'http://www.blogto.com/cafes/sonic', None, 'http://www.vantagegaragedoors.com', 'http://tnailslasvegas.com/', 'https://www.supercuts.com/locations/az/mesa/gilbert-gateway-town-center-haircuts-90179.html', '1592778824', 'http://www.goodwillsp.org/', 'http://purechiropracticfamilygilbertaz.com/custom_content/c_169735_about_us.html', 'http://sabrosos.ca', 'http://fringesalonlv.com/', None, None, 'http://www.palms.com/laguna-pool-house-kitchen.html?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.theonenaillounge.ca', 'http://SunLawAttorneys.com', 'http://www.earlhaig.ca/main.php', 'http://www.colordesignllc.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.seafishnchips.com/', 'http://www.levieuxfourmanago.com', 'https://amerisleep.com/retail/scottsdale-optima-camelview/', 'http://www.rivergambler.ca', 'https://bostonpizza.com/en/locations/ste-julie.html', 'http://www.hotdogdiner.com', 'http://www.mintindiancuisineaz.com', 'https://representatives.countryfinancial.com/mark.derrico', 'http://www.kormancompany.com', 'https://www.hometroniclv.com', 'http://www.northlandvillagemall.ca', None, 'https://www.foreveramorelv.com', None, 'http://www.cfaeauto.com', 'http://www.spielhaus.com', 'https://agents.allstate.com/joe-kennedy-chandler-az-1422670.html', None, 'https://www.extraspace.com/storage/facilities/us/arizona/peoria/900038/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.doublezeropizza.ca/downtown', 'http://nostalgicalley.com', None, None, None, 'http://georgeandsonsasiancuisine.com/', None, 'http://www.milkbarphoenix.com', 'http://www.cameroncreekapartmenthomes.com', 'http://www.buildingblockmasonryaz.com', 'http://www.lasvegasprosthetics.com', None, None, None, 'http://destinyderma.com', 'http://RedVapor.net', None, 'http://www.paradisebakery.com/store_indiv.php?stid=10', 'http://www.knithappensaz.com', 'http://www.dorfershoes.com', 'http://www.rougevegas.com', 'http://www.advantagefunerals.com/en-us/locations/melchers.page', None, 'http://dishfunctionallchefs.com', None, 'http://www.biltmoreproprint.com', 'http://www.charlottecellulardoctor.com', 'http://locations.goodcentssubs.com/ll/US/AZ/Glendale/4920-W_-Thunderbird-Rd_*-Ste_-102', 'http://www.juicycouture.com', 'https://www.torontosbestcleaningservices.com', '1592779041', 'http://www.ctcnevada.net', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, None, None, 'http://www.coleplumbingaz.com', None, 'http://eddyiggys.weebly.com/', 'http://www.mixturesrx.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.fellerorthodontics.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, 'http://www.moviedomes.com/', 'http://perfectairandpipe.com/', 'http://www.ip3repair.com', 'https://serene-nail-spa.business.site', 'http://www.vpicasso.com', None, 'http://www.deltaco.com', 'https://www.sail.ca/en/our-stores/etobicoke', None, '1592779127', 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=199&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-199', None, 'https://www.dickblick.com/stores/pennsylvania/pittsburgh/', 'http://www.keystonebuildinginspections.com', 'https://www.wildpcs.com', 'http://www.subway.com', None, None, 'http://www.genghisgrill.com/?utm_campaign=2603&utm_medium=listings&utm_source=Yelp', 'https://www.delta.com', None, None, 'http://www.sushirockohio.com', 'http://www.patientnetworks.ca/', None, None, None, 'https://locations.wendys.com/canada/qc/anjou/7295-des-galeries-danjou', 'http://www.thefilmbuff.com', None, None, None, 'http://www.fixcb.ca', 'http://www.torontodermatologycentre.com', 'http://www.blazinmongolianbbq.com', 'http://www.azvalleywidemovers.com', 'https://drumlinridgewinery.com', 'http://www.sircarpet.com', None, 'https://www.pawnamerica.com/13__madison', 'http://www.creativehomestagers.com/', None, 'http://www.labcorp.com', 'http://www.kamiyahairdressing.ca', None, 'http://smogbusters.com', '1592779247', None, 'https://www.fivestarelectricalservices.com', None, None, 'http://www.farsidebar.com', 'https://www.hungryhowies.com/store/hungry-howies-00630?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00630&utm_content=Website_Link', 'http://www.pacificsales.com/', None, None, None, 'http://www.reserverealtymanagement.com', 'http://servicetechniques.com', 'http://www.campbellssweets.com', 'http://www.onasalon.com', 'http://www.winners.ca/', 'http://www.capsgrill.com', 'https://www.dollar.bank/maps/index.aspx?branchId=1023&zipcode=44141', 'http://www.dtphxdental.com', 'https://locations.theupsstore.com/az/mesa/2753-e-broadway-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.marriott.com/hotels/travel/yyzri-residence-inn-toronto-airport', 'https://www.jayselznick.com', 'http://www.taubergsurgery.com', 'http://www.topnotchsalonandboutique.com', '1592779329', 'http://www.trattoriamercatto.ca', 'http://myazsmile.com', 'http://www.power88lv.com/', 'http://www.shopstonecrest.com', 'http://www.snmspalon.com', None, 'http://www.vegashomesre.com', None, '1592779359', None, 'https://www.gorelikdentistry.com', 'http://www.machinegunexperience.com', '1592779374', 'http://amcopoolservice.com', 'http://www.whittamoresfarm.com', 'http://www.johnvince.com/', 'https://www.roselleto.com', 'https://www.sierraexpeditions.com', 'https://savealot.com/grocery-stores/parma-44129-660', 'http://www.philsebastian.com', 'http://www.mintbeautyspa.com', None, None, None, 'http://www.thebagelhouse.ca', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, None, 'http://www.vhdental.com/', 'http://www.eyesiseyecare.ca', 'http://www.costcutters.com/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'https://www.longhornsteakhouse.com/locations/nh/concord/concord/5131?cmpid=br:lh_ag:ie_ch:dry_ca:LHQ121LOCURL_dt:20200619_sn:yelp_gt:concord-nh-5131_pl:locurl_rd:1094', 'http://www.poolsandspasaz.com', None, None, 'http://www.ddsdiscounts.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/11240+Perry+Highway+Route+19-Wexford-PA-15090/storeid=2449?cid=ps_ylp_2020', 'http://www.holidayflorist.net/?srccode=yelp_track', None, 'http://johnfishjewelers.vegas/', None, 'http://www.petdentalusa.com', 'http://www.westsidemarket.org/vendor.aspx?id=34', None, 'https://www.scottsdaleanimalhealthcare.com', None, '1592779486', '1592779491', 'http://storelocator.pepboys.com/pepboys/stores/scottsdale/scottsdale/00684', '1592779499', 'https://www.urbannecessities.com', 'http://www.alleventsproduction.com', 'http://www.hardrockhotel.com/las%2Dvegas/pool/skybar/', 'http://thaicuisine1.com', 'http://www.screenmobile.com/Phoenix-Southwest', 'http://www.terribleherbst.com/', 'https://www.jetspizza.com/stores/wisconsin/middleton/2831-parmenter?utm_source=Yelp-Ads&utm_medium=Yelp-Ads-SEO&utm_campaign=WI-005&utm_content=Website', 'http://www.chianticafe.ca', 'http://www.pjspet.com', 'http://lvteeth.com', 'https://www.sprint.com/storefronts/bd/sprint-mesa-az-85206-fcs-497/?ecid=SEO:Yelp:2020_Q1:LastMile', None, None, 'http://www.infusemedspa.com', None, 'http://www.fitnessworks.com/', None, 'https://www.kindercare.com/our-centers/mesa/az/300900?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=300900', 'http://www.epennzoil.com', None, None, None, 'http://www.azrootcanaldr.com', 'http://www.sincityyoga.com', 'http://blackcadillacsalonandbarber.com', None, 'http://www.alterationsmadison.com', 'http://www.theitalianmarketbuffet.com', 'http://www.cabanaonmill.com', 'http://www.joethemover.ca', 'http://www.brightonhotdogshoppes.com', None, 'https://www.nicksfurniture.com/locations/mesa.html', 'https://www.cilantrotaqueria.com', 'https://www.kindercare.com/our-centers/phoenix/az/301465?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=301465', 'http://suzyshier.com', 'http://skgrillnchill.com', 'http://corduroylv.com', 'http://www.blueberryhillrestaurants.com/', 'http://kaylorspools.com/', None, None, None, '1592779645', None, 'http://www.distinctive.net/', 'http://www.norterrapetnannies.com', 'http://www.carolinafootandankle.com', 'http://www.kbprecisionpainting.com', 'http://www.moldneutralizers.com', None, None, 'http://www.inkraftstudios.com', 'https://www.thegoldengate.biz', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/richmond-hill/yyzep/hoteldetail', 'https://www.chomedeyhyundai.com', 'http://techknowspace.com/', 'http://www.lickshomeburgers.com', 'https://www.rhpl.ca/node/120', 'http://www.corporatepresentation.net/', 'https://www.ulta.com/stores/las-vegas-nv-301', '1592779707', '1592779711', 'https://www.everbluetraining.com', 'http://phoenixyardpros.com/', 'http://www.Saxetheater.com', 'http://www.pandemonium.ca', 'https://greenwaysaddlery.com', None, 'http://www.verizonwireless.com/stores/north-carolina/charlotte/pineville-308497/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://locations.samash.com/nv/las-vegas/53/', 'http://www.azlaserdentistry.com', 'https://www.tireworks.net/locations/6455-south-pecos-road-las-vegas/', 'http://www.kahanoffconference.com', 'http://gusmarkia.wixsite.com/angelasrestaurant', 'http://www.montecarlo.com/pool-amenities/fitness.aspx', 'https://www.kent-law.org', '1592779762', None, 'https://www.shelterfurniture.ca', 'https://www.lifetime.life/life-time-locations/on-vaughan.html?utm_medium=directory&utm_source=yelp&utm_content=homepage', 'http://www.invitationhomes.com', 'http://www.theelitemovers.com/', None, 'http://amindfulnesslifecenter.com/', 'http://www.ycastrongsville.com', None, 'http://www.dignityhealth.org/medical-groups/nevada/', 'https://locations.stlouiswings.com/on-stouffville-stouffville', None, '1592779802', 'http://www.qualitytransmission.com', None, 'http://www.oreillyauto.com', 'https://www.originaljoes.ca', 'http://www.serenityautobody.com', 'http://www.clevelandbeercellars.com', None, 'https://www.allstarbailbondslv.com/henderson/', 'http://www.sbarro.com/locations/toronto-eaton-center/', 'http://www.planet21salon.com/location/the-arboretum/', 'http://www.itsmyparty.com', 'http://teshurt.com', None, 'http://www.dooneys.com', None, 'http://fazildp.wix.com/henna-art', None, '1592779870', 'http://www.stonemanclimbing.com', None, 'http://atredchina.weebly.com', 'https://pelicanssnoballs.com/locations/nc/belmont/70/', 'http://trapezius.net', 'http://www.runningroom.com/', 'http://www.firkinpubs.com/pubs/falcon-and-firkin', 'http://www.dosummers.com', None, None, None, 'http://www.toppers.com/', None, 'https://www.overlandblueprint.com', '1592779920', None, 'http://www.frontgate.com/', None, 'http://www.flowhairsocietyaveda.com/', None, 'http://www.peteuthanasia.xyz/', 'http://www.canyonridgeperio.com/', None, 'http://Momentum-Tickets.com', 'http://www.costcutters.com/', 'http://www.valueworld.net/', None, None, None, 'http://www.floridacafecuban.com/', 'http://www.ladycpa.com/', None, '1592779979', 'https://candachihair.business.site', 'http://www.karamia.ca/', None, '1592779993', 'http://hangar9az.com', None, 'http://arisra.com/', 'http://www.furio.tv/', 'http://www.daysinn.com', None, 'https://www.canada-storage.com/self-storage/toronto-west', 'http://www.baciitalianbistro.com', 'http://onceuponatimetoys.com', 'https://www.ncsecu.org', None, 'http://www.LMartinTaylor.com', 'http://www.avenue.com/on/demandware.store/Sites-Avenue-Site/en_US/Stores-Details?storeID=667&requestType=normal', 'https://www.bindingpros.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', 'http://splendidchinamall.ca/en/store_detail.php?id=48', '1592780055', None, 'http://www.destinationxl.com/mens-big-and-tall-store/storelocator/storeDetails.jsp?storeNumber=+9716', 'http://www.scoresbyfamilylaw.com', '1592780070', 'http://www.intlacademyaz.com', 'http://www.iconicplumbingaz.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.umailshipping.com', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', None, 'http://www.anaboutique.net', None, 'http://www.express.com', 'http://www.integritypainaz.com', 'http://www.Salonkneo.com', 'https://www.thefurnitureservice.com', 'http://pittsburghcafe.com', 'https://www.doggiedistrictaz.com?utm_source=yelp&utm_medium=social', None, 'http://www.verduresalon.com', 'https://stew-keene-revelation-real-estate.business.site', None, None, None, 'http://www.motel6.com', None, 'http://mrthai.ca/concord/', 'http://www.madefoods.com', 'http://theflyerguysaz.com', None, 'https://www.discounttire.com/store/nv/henderson/s/1300?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'https://www.hardees.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, 'http://renforthvet.com', 'http://www.fictionclub.ca/', 'http://www.terravita.com', None, '1592833289', None, None, None, None, 'https://fixautousa.com/phoenix-sky-harbor', 'http://www.paulsacehardware.com', 'http://www.clearsound.co', 'http://www.silladesigns.com', 'https://libertyremodelingllc.com', 'http://www.bowlology.com', '1592833324', 'https://sundevilclean.com', 'http://www.chachis.ca', 'http://www.justwhiteshirts.com', 'https://www.chick-fil-a.com/yongeandbloor', 'http://www.moombatheater.com', None, 'https://www.planetfitness.com/gyms/north-randall-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'https://talentbridge.com/charlotte/', 'http://www.fastfreshfoods.ca/', '1592833358', 'http://www.merrymaidssoutheasttoronto.ca/', 'https://wowair.us', 'http://www.allaboutserving.com/?page=tempe', 'http://somersaultletterpress.com', 'http://www.kidsfuncity.ca/', '1592833381', 'https://www.gowireless.com/stores/az/tempe/tempe-rural-road/', 'https://www.kohls.com/stores/az/mesa-749.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.gjwaterproofing.net', 'http://www.akco.ca/', 'https://www.jaycfoods.com/topic/ruler-foods', 'https://theannex.com', 'http://www.concordparkwayanimal.vetsuite.com', 'http://www.poutinedaretobefresh.ca', '1592833415', 'http://www.eastofchicago.com/', 'http://www.sleepoverrover.com', 'http://www.melodysmassage.com', 'https://www.mvpplumbingpro.net', 'http://www.SkinEnvyLV.com', '1592833435', 'https://www.tmdretail.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.cox.com/local/residential/stores/nv/henderson/545-marks-street?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q102', 'http://www.bark5thave.com', 'https://butterblockyyc.com', 'http://www.bootycampfitness.com', 'http://www.bluefighookah.com/', 'https://www.skycourtharbors.com', None, 'http://www.lkqcorp.com/en-us/locations/lkq-of-arizona-phoenix-az.aspx', 'https://www.mattressfirm.com/stores/sc/rockhill/mattress-stores-rock-hill-sc-29732-8431.html', 'http://www.sportstherapycaire.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://rochellispizzahouse.com/', None, None, 'http://www.interconnectionstherapy.org', 'http://www.CompleteCareObgyn.com', 'http://www.eatnpark.com/aboutus_hospitality_park.asp', None, 'http://www.vlashed.com', None, None, 'https://mcgilvrayvet.com', None, None, None, None, 'http://fitlifefusion.com', 'http://www.lvcvt.com', 'http://www.usautobodyandpaint.com/home.html', 'http://www.luckymoonpies.com', 'http://www.commissobakery.com/', 'http://www.dreamcarslasvegas.com/', 'http://www.brospizzaco.com', None, 'http://www.bigcreekpet.com', 'http://www.pdqstores.com/gmaps/Wisconsin/MadisonArea/131.html', 'http://www.rosecitykitchen.com/', None, 'http://www.thedakotatavern.com', 'https://insomniacookies.com/locations/store/1148', 'http://www.desertrat.com', 'http://www.californiasalads.com', 'http://www.gamezoneusa.com', None, 'http://www.hotyogau.com', 'http://www.jabzboxing.com/tempe', 'https://locations.wendys.com/united-states/oh/cleveland/13939-euclid-ave.', '1592833587', None, 'http://www.ginospizza.ca/', 'http://www.goodwillsocal.org/', 'http://www.HousesNv.com', 'http://www.superlube.com', None, 'http://www.assuredpool.com', None, None, 'http://freaknbrew.com/', None, None, '1592833619', 'http://www.thewoodsrestaurant.com', None, 'http://www.odar.ca', 'https://www.stellaresto.com', 'http://www.vickiefalen.com?cmpid=cu6h_blm_0006', 'https://locations.wendys.com/united-states/nc/indian-trail/13810-independence-blvd', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, '1592833640', None, 'http://www.motorlandautosales.ca', 'http://www.theframingdepot.com/', 'http://www.702tattoo.com/', 'http://www.discountaquariumsaz.com', 'http://www.jewelrybuyersoflasvegas.com', 'http://prohibitionpastries.com', 'http://www.nafence.com', 'https://www.moes.com/find-a-moes/ohio/north_olmsted/642?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://www.citrusapartmentslv.com/', 'http://www.gvsconstructionllc.com', 'http://signaturesmilesvegas.com', 'http://www.chefydrews.com', 'http://www.scottscoachworks.com', None, 'https://business.google.com/website_shared/launch_bw.html?f=vegas-noodle-house.business.site', 'http://louiecoffee.com', 'http://www.local1794.ca/', 'http://www.westsidehairstudio.ca/', 'http://www.revolutionsproshop.com/default.aspx', 'http://a40autobody.com', 'http://www.calicojacksglendale.com', 'https://www.petenelsons.com', 'http://www.unlimitedsmiles.com/office-phoenix.html', None, None, 'https://www.publicstorage.com/arizona/self-storage-gilbert-az/85233-self-storage/850?pid=wyelp&CID=1245&CHID=AFL', 'https://www.americandiscountfoodsaz.com', None, 'http://www.melissaainsworth.com', 'http://www.restaurantchezparra.com/', None, 'http://www.artfulnaturedecor.com', 'http://goglassinc.com/index2.html', None, 'http://www.revitasize.ca/', None, None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89128/027192/', None, 'http://columbiafence.info', 'http://www.concentra.com', 'https://www.popeyes.com', None, 'http://earlscourtbbq.com', 'http://www.stvincentdepaulchurch.com', None, None, None, 'http://www.phoenixcoffee.com', 'https://www.godsgardentreasures.com', 'http://scramblersrestaurants.com', '1592833772', 'http://crafthomedecor.com', 'https://order.dominos.ca/', None, None, 'http://www.12throundfit.com', 'http://www.rgheating.com', 'https://www.esso.ca', 'http://www.barpalco.com/', 'http://www.newyorkfries.com', 'http://www.dentistryatwestland.com', None, 'http://www.cwd.org/community/events/willy-street-fair/', 'https://www.famousfootwear.com/?partnerid=YELP', None, 'https://ncfreemovingquote.com/movers-charlotte-nc/', 'https://www.hanrattylawgroup.com', 'http://www.steaknshake.com/locations/23817-steak-n-shake-cascade-crossing-brooklyn', '1592833816', 'http://bclibrary.org', 'http://bbqgrillcleaners.com', 'http://www.bouncenplay.ca', '1592833828', None, 'http://www.harvest-restaurant.com', 'http://www.bambinispizzeria.com', 'http://www.cinemathequeontario.ca', 'http://www.northernsmilesdentistry.com/', None, 'http://www.coincarwash.ca', None, None, 'https://landroverthornhill.ca', '1592833854', 'http://www.happypandatoys.com', '1592833860', 'http://www.safeway.com', 'https://www.jerseymikes.com/29008', 'http://thefry.ca', 'https://www.clevelandmonsters.com', None, 'http://palmettoskinandlasercenter.com', 'http://www.rayspizzaaz.com', None, None, None, 'http://www.7-eleven.com/?yelp=29641', None, None, 'http://www.702rcraceway.com', None, None, 'http://nvpainrelief.com', 'https://www.colorpointautobody.com', None, 'http://www.campk-9resort.com', 'http://www.arizonarug.com', None, 'http://www.maximspizzacatering.com', None, 'http://www.plusprinting.ca/index.html', 'https://www.currys.com', 'http://www.diamondgraniteaz.com', 'http://vegascarpetcleaningpros.com/', 'http://www.talbots.com', None, None, 'https://order.pizzapatron.com/menu/avondale-dysart-rd?utm_source=Yelp&utm_medium=Order&utm_campaign=Ordering', 'http://www.verdeattrilogy.com/verde_grill/', None, 'https://innovativeplumbingpros.com/henderson-nv-plumbers-henderson-plumbing-repair-services-company/', 'http://www.brontecollege.ca', 'https://www.wyndhamhotels.com/hotel/15056?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:15056', None, 'http://www.robertsresorts.com/resorts/pueblo-el-mirage', 'http://arizonabestflooring.com/', 'http://www.ljsilvers.com', 'http://thedriftwoodgroup.com/restaurants/washington-place-bistro-inn', 'http://www.purehealthycosmeticspa.com', 'http://www.bonkerscafe.net', 'http://desiredhandyman.com', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700006431964415&ds_s_kwgid=58700000442923194&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', '1592833980', 'http://www.gap.com?tid=gpme000290', None, '1592833988', 'http://www.thesmilingbuddha.ca', 'http://www.burgerking.ca', 'http://mainstreetpizzerianc.com', 'http://www.mononafarmersmarket.com/', 'http://beirutstreetfood.ca', 'http://www.burton.com', 'http://www.thecaptainscap.com', None, 'http://www.mysticlandscapes.com/', 'http://www.ohanasalonaz.com/', None, '1592834021', 'https://www.quadrealres.com/apartments/on/north-york/bayview-mews/', None, 'http://www.sunnysbridestobe.net', None, None, 'http://www.shearexcitementhairsalon.com', None, None, 'https://www.ganleyhonda.com', 'https://www.summitcreditunion.com/?utm_medium=location&utm_source=yext', 'http://www.siegelsuites.com', 'http://www.elsalutongbahay.com', None, 'https://locations.theupsstore.com/az/cave-creek/29455-n-cave-creek-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.myfoodcity.com/', '1592834059', 'http://www.roysebrinkmeyer.com', 'http://www.dgministorage.com', 'https://www.carrabbas.com/locations/nc/huntersville?utm_source=yelp&medium=social&utm_campaign=location_listings', 'http://www.sonicdrivein.com/', None, 'http://310dustcontrol.com', None, 'http://www.after-4.com', 'http://zellaspizza.com', 'http://www.bellatoccare.com', 'http://www.mhmlv.com', 'http://www.onceuponachildinrobinson.com', None, None, 'https://www.marcs.com/stores/marcs-middleburg-hts-southland-grocery-store-4413', 'https://ladycleather.com', 'http://www.steaknshake.com/locations/23831-steak-n-shake-diamond-center-drive-mentor', None, None, 'http://torontoislandbicyclerental.com', 'http://www.trooncc.com', 'http://www.enterprisecarsales.com/location/5072/Enterprise_Car_Sales_San%20Tan?mcid=iyp:277&CUR=yelp', 'http://www.junors.com/store/', 'http://bmv.ohio.gov/18.stm', 'http://precisioneyeconcord.com', 'http://www.crossroadsvh.com/', None, 'http://www.danceteq.com/', 'http://ananekebeautysalon.com', None, 'http://www.hojo.com/hotels/hotel-overview?hotel_id=46021&cid=whg_hj_yelp&wid=ps:addppc_yelp&tel=18008899735&reg=appc-_-ylPROPP-_-46021-_-hjnat', 'http://www.ricardosoflasvegas.com', 'https://www.ubreakifix.com/locations/superstitionsprings', None, None, 'https://www.howlatthemoon.com/pittsburgh/', 'http://oakmonthome.com', 'https://www.carolinacopperhvac.com', 'http://www.fidelgastro.ca/', 'http://www.partiesonpurpose.com', 'http://www.fasgas.ca', None, 'http://www.madisonsouthpark.com', 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/lakewood-hospital', 'http://www.nvccf.org', None, 'http://www.centerforpainandsupportivecare.com', 'http://klostersbutchershop.com', 'https://www.anthropologie.com/anthro/store-locator/store/calgary/chinook-centre/00549', None, 'https://www.familydentalcarechampaign.com', 'http://www.lougheedhouse.com', 'http://www.fresh52.com', 'http://888xboxfix.com/', None, 'http://www.fibercreations.com/', 'http://www.trinitygallery.ca/', None, 'http://www.vetinmississauga.com', '1592834211', 'http://www.summerlincrossfit.com', 'http://www.freshcollective.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'https://storage.makespace.com/yelp', None, None, 'http://medpost.com/location/peoria-az', 'http://www.tradingacademy.com/charlotte/', 'https://carylbakervisage.com/pages/vaughan-mills', None, 'https://www.planetfitness.com/gyms/west-mifflin-pa?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://asasushi.com', 'https://www.beautifulsmilesdentalspa.com', 'https://www.aaautocarelv.com/locations/aa-auto-care-sunset-rd/', 'https://phoenixpianomoving.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://themintdispensary.com', None, None, None, 'http://www.chinahutnv.com', 'http://www.bigfunbigfun.com', 'http://www.trulyindia.ca', 'https://www.westernpizzaexpress.ca', None, 'http://www.marriott.com/hotels/travel/phxas-fairfield-inn-and-suites-phoenix-midtown', '1592834284', None, 'http://DirectToYouIV.com', '1592834296', 'https://thesonoran.mgproperties.com', None, 'http://fortunahairsalon.com', 'https://www.smartstyle.com/en-us/locations/az/glendale/located-inside-walmart-3241-haircuts-11041.html', 'https://www.greulichs.com', 'http://www.columbiahillsgolf.com', None, None, 'http://www.eawraps.com', 'http://www.pjonesfh.com', None, None, None, None, None, 'http://www.greenbulldog.net', 'http://www.kidsfuntown.ca', 'http://www.360physicaltherapy.com/locations/physical-therapy-Sun-Lakes/', '1592834362', 'https://nationwidevision.com/locations', None, 'https://www.racersportif.com', 'http://nocegourmetpizza.com', 'http://www.expresswaymovers.ca', 'http://drsobek.com/', 'http://www.dazzlenailspa.com', None, 'http://www.fun-n-stuff.com', 'https://www.kungfuforlife.ca', 'https://www.americandecoralv.com', 'http://www.hotyogawellnesswoodbridge.com/index.php', 'https://www.searsauto.com/stores/6661?psid=campaigncode-6661', 'http://www.rjmccarthy.com/', None, None, 'http://www.beckers-donutsandbakery.com', None, 'http://www.destinysbride.com', 'http://www.downtownlocksmith.com', None, 'https://www.walmart.com/store/3293/chardon-oh/whats-new', 'https://www.nofrills.ca/store-locator/Angelou%27s+nofrills+%28Creditview+Rd%29/3454?storeId=3454', None, '1592834448', None, 'http://www.patatepersil.com', None, 'http://www.mathnasium.com/summerlin', 'http://www.gibsonair.com', None, 'https://www.walmart.com/store/5497/evans-mills-ny/whats-new', 'http://www.ediblephoenix.com/', 'http://www.royfosswoodbridge.com/', 'http://livingwellchiroaz.com/', 'http://www.galatravels.com', 'http://www.echospaandsalon.com', 'http://enzosgvpizza.com', 'http://theanneboleyn.ca', 'http://www.hhpetspa.com', None, 'http://www.brunkeglass.com', 'http://www.ultimatecarpetrepair.com/', 'http://www.threeriversautoglass.com', None, 'http://www.Fitness4Home.com', 'http://www.pottershouserx.com/', None, 'https://www.palnv.org', 'https://www.chapmanbmwoncamelback.com', None, None, 'https://pawn1st.net/our-locations/tempe-pawn-shop-title-loans-jewelry-buyers-234-west-southern-avenue-tempe-az-85282-480-894-8666/', None, 'http://howbowda.com/', 'http://www.mysisterscloset.com', 'https://rooterman.com/las-vegas/', 'http://www.greatclips.com', '1592834588', 'http://www.restaurantdepot.com/', 'http://www.azautoair.com', 'http://toprockertattoos.com', 'https://locations.theupsstore.com/az/avondale/11435-w-buckeye-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.patiostaraz.com', '1592834612', 'http://www.automatictransmissionexperts.com/', '1592834620', None, None, 'http://www.sedonaspas.com', 'https://strongishappy.com', 'http://www.na-siam.ca', 'http://museumofcontemporaryart.ca', None, None, 'http://www.rwc.org/?utm_source=Yelp&utm_medium=web%C3%8A', None, 'http://terminix.com', None, 'http://mcldaz.org/southeast', None, None, 'http://lakewood-luxury-consignment.business.site', None, 'http://www.chatime.com', 'http://www.modshairmtl.com', 'http://www.clydessalon.com/', 'http://www.pizzapizza.ca', None, 'http://www.northcrosseye.com', 'http://www.sunvalleyarthritiscenter.com', 'http://www.theblakehouse.ca', None, 'http://www.lascasitasapthomes.com', 'https://ballantynefamilydental.com', 'http://med.unr.edu/las-vegas', 'http://www.myohiogi.com/addc', 'http://www.cobsbread.com', 'http://www.lvcrownmoulding.com/', None, 'http://www.barkingduckbrew.com/main.html', 'http://www.bittersweetcakeboutique.com/Contact-Us.html', None, 'http://www.petsgopetcare.ca', None, 'http://www.stvincentdepaul.net', 'http://airparkautoclinic.com', 'http://legirls.net', None, 'http://www.exodusoh.com', 'http://promedhealthnc.com/', 'http://bloketoronto.ca', None, None, None, 'http://www.vicandanthonys.com/locations/las-vegas/index.asp', None, 'http://headhuntershomesalon.com', 'http://www.carlittasdayspa.com/', 'http://boxbros.com', None, 'http://www.pardons.org', 'http://www.ladiesoflineage.com', 'https://www.nationalsports.com/pages/store-newmarket-ontario', 'http://www.thymetherestaurant.com/', 'http://www.frysfood.com', None, 'http://www.realtyamerica.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.1caclean.com', 'http://www.budgetblinds.com', None, None, None, 'http://www.icelandair.ca', 'http://amyjonesgroup.com', 'https://dandydrycleaners.com', 'https://www.blacklightslide.com', None, 'http://www.pachuco.ca', 'http://www.thedoordoctoraz.com', None, 'http://www.boaden.com', 'http://www.mardaloopvet.ca', 'https://mezgouf.ca', 'http://www.drmazaheri.com', None, 'http://www.whiskersdogspa.com', None, None, 'http://jerkbbqhaven.com', None, None, None, None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.abitofhome.ca', 'http://chick-a-dees.net/', 'http://www.starbucks.com', 'http://www.voiceamerica.com', 'http://www.sheibanjewelers.com', 'http://www.starbucks.com/store/17296/', 'http://autoburgerandfryguys.com/', None, None, None, 'https://manchuwok.com', 'http://enfuegolasvegas.com', 'http://www.renton702.com', 'http://www.gosfm.com/', None, 'http://www.goodwill.org', 'http://nigerianfoodlv.com', 'http://www.firebirdraceway.com/', 'https://www.portstoronto.com/airport.aspx', 'http://www.noircoffeeandtea.com', 'http://liquorlane.ca', 'https://www.walgreens.com/locator/walgreens-1725+northport+dr-madison-wi-53704/id=2967', '1592835016', 'http://www.escapethislive.com/phoenix', 'http://www.yolandashairdesign.com', 'http://kidneypuncher.com/', 'http://www.peets.com/?cm_mmc=yelp*peets*8_28_12_homepage*na', 'http://Www.mesahookah.com', 'https://www.emser.com', 'http://happygarden.food94.com', 'https://www.pthealth.ca/clinic/central-scarborough-physiotherapy-clinic/?ibp-adgroup=yelp&utm_campaign=premium-listing&utm_source=yelp&utm_medium=directory', 'http://www.ariaremodeling.com', 'http://tothpainting.com', 'http://iphix.ca', 'https://www.fyzical.com/las-vegas/pecos', 'http://www.plazaappliancemart.com', 'http://www.bgood.com', None, None, 'http://www.azcentralcu.org/home/home/?utm_campaign=ACC-YELP&utm_medium=LocalSearch&utm_source=YELP', 'https://elementsmassage.com/yelp-herbal-ritual-special?loc=Wexford', 'https://www.allnevadainsurance.com', 'https://www.kemurilounge.ca', 'http://www.midoco.ca', None, 'http://www.escaperisknc.com', 'https://provinyl.solutions', 'http://www.azqpools.net', 'http://www.roamingfork.net', 'http://www.bepicathletics.com', 'https://www.wingstop.com/location/wingstop-422-chandler-az-85226/menu', None, None, 'http://www.posaresalons.com', 'http://www.royalcareoptical.com', 'http://www.mobile-massage-lasvegas.com', 'https://www.elephantcastle.com', 'http://sdhairstudio.com/', '1592835147', None, 'http://www.studiobsmiles.com', None, None, 'http://www.tsmower.com', 'https://www.poshsalonnspa.com', None, 'http://www.diysmokeshop.com', 'http://www.csnwine.com/', 'http://www.clevelandyellowcab.com', 'http://emilneaguco.com/', 'http://www.winebutler.ca', 'http://theshozanroom.com/contact/', 'http://www.nxsremodeling.com', 'http://www.capsulemusic.com', None, None, 'http://doubletree3.hilton.com/en/hotels/ohio/doubletree-by-hilton-hotel-cleveland-downtown-lakeside-CLELSDT/index.html', 'http://pigtailsandcrewcuts.com/charlotte-cotswold', 'http://www.ave25.com', None, 'http://www.hennejewelers.com', 'http://www.bk.com', '1592835235', '1592835238', None, None, 'https://www.expressoil.com/stores/concord/nc/6150/', 'http://calgaryweatherdek.com', 'http://lasvegashappyfeet.com', 'https://www.cosmopolitanlasvegas.com', 'http://friendshipcmhc.org', 'http://www.lvinspect.com', None, '1592835270', 'http://www.gametruck.com', 'http://www.tiffany.ca', 'http://www.copps.com', 'http://www.blackrockcoffeebar.com', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1386&s_cid=lsl0000001', None, 'https://pncpittsburgh.catertrax.com/upload/EcoBistroweeklymenu.pdf?intOrderID=&intCustomerID=', 'http://www.luckypawsaz.org', None, None, 'http://www.quiznos.com/', 'http://budgetlasvegas.com', 'http://www.etalimos.com', 'http://danshardwoodflooring.com', None, '1592835323', '1592835327', None, 'http://www.bobspopcorn.com', '1592835336', '1592835341', None, 'https://www.budget.com', 'http://www.dtlvevents.com', None, None, 'http://www.neighborhoodwatchsecurityphx.com', '1592835364', 'http://www.curlambassadors.ca/curly-hair-salon-pickering/', None, '1592835373', 'http://locations.harristeeter.com/nc/charlotte/205/', 'https://littlewhitetooth.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.publicstorage.com/arizona/self-storage-scottsdale-az/85260-self-storage/1342?pid=wyelp&CID=1245&CHID=AFL', 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', 'http://www.havanacastlecigars.ca', 'http://www.stationsquare.com/store/dirty-harrys/2137033649/2138800020', 'https://www.citychurchonline.org', None, 'http://www.coffeebean.com', 'http://fifthsocialclub.thefifth.com', 'http://olenliving.com/communities/nevada/morningstar', None, 'http://sheardesiresalon.com/', 'http://www.quiznos.com', None, None, None, 'https://vanhornepizzeria.com', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://www.bestwestern.com/en_US/book/hotel-rooms.03062.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03062', 'http://www.rubberduckydetail.com', 'https://www.liceclinicssouthcharlotte.com', None, None, '1592835461', 'http://www.fairleyspainting.com', 'https://www.directtoolsoutlet.com/', 'https://www.hot-and-sour.com', 'http://reddragonmenu.com', None, 'http://www.acehardware.com/store-details/11394', 'http://secondopinionplumbingaz.com', None, 'https://www.drkenlepinskas.com', None, 'http://www.buyncell.ca', 'http://www.trysports.com', '1592835502', 'http://www.pghgrille.com', None, 'https://www.infamouspoolcare.com', None, None, None, 'http://www.tommyspastries.com', 'http://www.bookcity.ca', 'http://www.didyouplan.com?cmpid=d017_blm_0006', 'https://www.hilton.com/en/hotels/yyzaphf-hilton-toronto-markham-suites-conference-centre-and-spa/?SEO_id=YELP-HI-YYZAPHF', 'http://locations.harristeeter.com/nc/charlotte/205/', '1592835540', 'http://www.completeprintshop.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.horizonvet.ca', None, None, 'http://www.starbucks.ca', None, None, 'http://www.grantsappliancerepairllc.com/', 'http://www.lssnv.org', 'http://shop.theclubairportlounges.com/the-club-phx-terminal-4-p/phx001.htm', 'https://www.sweetlemonadephotography.com', '1592835586', None, None, 'https://azcdps.com/locations/scottsdale/', 'http://www.sogojapaneseseafoodandsteakhouse.com', 'https://www.archerdental.ca/locations/archer-dental-littleitaly/', 'http://www.shultsfordwexford.com', 'http://www.arriveinstyleaz.com', None, 'http://www.primalsoup.ca/', 'http://smokespoutinerie.com', 'http://www.zapizzabistro.com', 'http://www.accuracygunshop.com/', 'http://www.eyelasheslasvegas.com', None, 'http://www.iansautointeriors.com', 'https://mitchellshomemade.com', 'http://www.johnsonfitness.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/9040+Mentor+Avenue-Mentor-OH-44060/storeid=3326?cid=ps_ylp_2020', 'http://store-locator.barnesandnoble.com/store/2243', 'https://www.mercedes-benz-newmarket.ca', 'http://Workshoppgh.com', 'http://www.starbucks.com/store/9298/', 'https://www.babybirdelectric.com', None, None, 'https://www.gerbercollision.com/locations/las-vegas-decatur-blvd-nv', None, 'http://majorleaguecollision.com/', 'https://www.familyfirstchiropractor.com', 'http://sitmeanssit.com/dog-training-mu/dog-training-pittsburgh/', 'https://www.fitwithkelly.com', 'http://www.lasvegasflooring.com', None, 'http://www.totalwine.com/store-info/nevada-las-vegas-summerlin/1201', 'http://www.hitesfh.com', 'http://lenasrotianddoubles.ca', None, None, 'https://www.haircutmengilbertmesaaz.com', 'http://www.budget.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.azadvancedhealthservices.com', None, 'http://Ebenezergrill.com', 'https://www.t-mobile.com/store-locator/az/avondale/99th-mcdowell?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://tatianabanquethall.com', 'http://www.aamconlv.com', 'https://www.unlocklasvegas.com', None, 'http://www.familydeli-bethelpark.com', 'https://www.spierandmackay.com', 'http://www.umisushiohio.com', 'https://www.nespresso.com', None, 'http://atomickoi.com', 'http://www.dhssignservice.com', 'http://rikkochez.ca', 'http://libertymd.ca', 'http://www.spokenspin.com', None, 'https://malleys.com/stores/wilson-mills/', 'https://local.safeway.com/safeway/az/phoenix/810-e-glendale-ave.html', 'http://www.urbinz.com', None, 'http://youngtowndentureclinic.com', None, 'https://www.avanatempe.com', 'http://LasVegasMold.com/', None, None, 'https://www.alaskausa.org', 'http://www.melonhead.ca', 'http://graduatetempe.com/', 'http://www.verizonwireless.com/stores/illinois/champaign/champaign-202336/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, None, 'https://dealer.sprint.com/maycom-communications', 'https://goodyearchiropractic.com', 'http://tiltontradenc.com', '1592835874', None, 'http://www.thecookiestore.net/', 'https://www.paramountfinefoods.com', 'http://www.cheapjoes.com/retail_outlet/charlotte-outlet-store.asp', 'https://twomenandatruck.com/movers/az/phoenix/west-valley', None, None, None, None, 'http://www.thelightvegas.com?utm_source=yelp', 'http://www.SandyMargolin.com', None, None, 'http://www.naturahealthimc.com/', 'https://www.londondrugs.com/london-drugs-store-030-calgary/heritage-plaza-030.html', None, 'http://www.downtowncocktailroom.com/', 'http://www.eatatmittys.com', 'http://www.jjonesjewelers.com', None, 'http://www.universaltaxlv.com', 'http://www.GD4K.COM', 'http://alcoaz.com', None, 'http://www.pvhomed.com/locations/scottsdale/', '1592835959', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://lvmpd.com/', 'http://www.clevelandymca.org/french-creek-avon.html', 'https://soswaxlv.com', 'http://www.superchunk.me', 'https://www.ihop.com/en/restaurants-phoenix-az/5020-e-ray-rd-1508', None, 'http://beartreesvc.com', 'https://www.brentsirrigationrepair.com', None, None, 'http://www.gemsetter.com', 'http://www.empowerpt.com', 'http://www.thelofthairsalon.net', 'https://locations.postnet.com/az/surprise/14537-w-grand-ave', 'https://www.applestorage.com/self-storage-units/toronto-downtown-on', None, 'https://www.protectmywater.com', 'http://vegasrockstarvip.com', 'http://groupeadonis.ca', None, 'http://www.gelatomessina.com', 'https://www.jaycfoods.com/topic/ruler-foods', 'http://www.printoriumtoronto.ca', 'http://www.azfertility.com', 'http://www.cavecreekpets.com/', 'http://ztejas.com/tempe-arizona-mexican-restaurant/', 'https://www.thehomeloancloser.com', 'http://www.redat28th.com', 'http://www.autocollections.com', 'https://locations.massageenvy.com/nevada/las-vegas/5643-centennial-center-blvd-ste-135.html', 'https://www.180smoke.ca/vape-store-180-smoke-bramalea-city-centre-brampton-e-cigarettes', 'http://byblosuptown.com', None, 'http://www.esimaging.net', None, None, 'https://www.hatterandhareaz.com', None, None, None, 'http://noodlecat.com', 'http://www.201westapts.com/', 'http://www.phoenix.gov/jury', 'http://www.modernnailslv.com', 'http://phoenixlandscapingandpools.com', '1592836117', 'http://www.mezbaanindiancuisine.com/', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'https://karahipoint.com', 'http://www.renewinglife.net/', '1592836138', 'http://conniesjewelrygalleryandclockshop.com/', 'http://www.vegasvinylrecords.com/', None, 'http://www.24hourfitness.com/FindClubDetail.do?clubid=203', 'https://www.dufflet.com', 'http://www.HS-UC.org', 'http://www.starbucks.com/store/12782/', None, None, 'http://mizukiteriyaki.com/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'https://www.cirquedusoleil.com/usa/las-vegas/deals', 'http://www.pizzahut.com/', None, 'http://www.gprespm.com', None, 'http://www.noahhelps.org/locations/heuser-family-medicine/', None, 'https://itea-one.business.site', None, None, 'http://locations.abm.com/oh/cleveland/facility-services-cleveland-oh-965.html', 'http://www.stayhealthylasvegas.com/retailer/store_templates/shell_id_1.asp?storeID=B61E453C98424C14B3938AD007ECA762', 'http://www.lakeviewvetclinic.com', 'https://www.ridenownorthvalley.com', 'http://www.intmontessori.com', None, 'http://www.gogreenzebra.com', 'http://www.costco.com', 'http://www.powerrvz.com', 'http://www.californiathai.ca', None, 'https://www.abbottscustard.com', 'http://www.vaughanpl.info/libraries/view/7', 'http://www.silvestrosdepotcafe.com', 'http://www.canadiantire.ca/en', 'http://www.digestifscottsdale.com', 'http://www.builtinbloomfield.com/index2.html', 'https://www.swimco.com/?utm_campaign=Market&utm_source=YELP', None, 'http://www.sushishop.com/', None, 'http://www.carefreestation.com/', 'http://pawsparesortpittsburgh.com', 'http://beyondblessedautotruckrepair.business.site', None, None, 'http://www.demirjiandesign.com', 'http://www.toronto.suttonplace.com/', 'http://www.langleydentalnc.com', None, 'http://www.caboautosales.vegas', None, 'http://www.frenchmellc.com', 'http://www.bk.com', 'http://www.tacobell.ca', 'http://www.walmart.ca/en/walmart-ajax-supercentre/3001', 'http://www.shuttershaque.com', 'http://www.jastalplumbing.com', 'http://www.theroundbistro.com', 'http://www.blockbuster.com', 'http://www.angelabeautyparlor.com', 'http://autoexpertscalgary.ca', 'http://vickynailsstudioandspa.com', 'http://www.ahandymandan.com', 'http://www.charlottepublicgolf.com/paradise-valley.php', 'http://peartreerestaurant.ca', '1592836385', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'https://fixautousa.com/las-vegas-central', None, 'https://stores.golfgalaxy.com/nc/charlotte/3039/', None, None, '1592836412', 'https://locations.jackinthebox.com/us/az/scottsdale/20385-n-hayden-rd', 'http://www.raggahairandbeautysupply.com', None, 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'http://www.provechoaz.com', 'https://www.marriott.com/hotels/photo-tours.mi?marshaCode=phxtm&pageID=HWRAL&imageID=5', None, 'http://www.valleygates.com', None, None, 'https://charlotte.funtasticks.com', None, None, 'https://www.dollar.com/locations/localsites/montreal', 'http://sparkyscreamery.com/', None, None, 'http://www.southendvet.com', 'http://www.ganzhauf.com', 'http://www.eyecandyopticiansltd.com', None, 'https://www.tgifridays.com/locations/1547/fridays-clevelandstrongsville-ohio', None, None, 'https://silvertoncasino.com', 'http://bridgevilleanimalhospital.com/', 'http://www.foodcity.com', 'http://www.scottsdalefamilydental.net', 'http://redbeardspgh.com/', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.izutoronto.com/', 'http://www.lloftylashes.com', 'http://miracletouchsd.webs.com', 'http://www.big5sportinggoods.com', None, 'https://elitetaxicabaz.com/', 'http://www.modernloveaz.com', None, 'http://dessaules.com', 'http://www.lush.com/', None, 'http://www.frostgelato.com', 'http://www.reactdefense.com/', 'http://www.rewardsnetwork.com/kennedytavern', 'https://preludeatthepark.mgproperties.com', None, 'https://www.discounttire.com/store/az/mesa/s/1294?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://toothclubforkids.com', 'https://pieology.com/?utm_source=yelp&utm_campaign=remarketing&utm_medium=cpc%C3%8A', None, None, 'http://www.partybustoronto.com', None, 'http://countytreeserviceinc.com', '1592838386', None, 'https://www.jerseymikes.com/2068', 'http://www.mcmathrealty.com/', None, 'https://www.thecoreinstitute.com', 'https://www.culinarydropout.com', None, None, None, None, None, 'http://www.waypointhomes.com', None, 'https://local.safeway.com/safeway/az/phoenix/3132-e-camelback-rd.html', None, 'https://www.savegcafe.ca', 'https://www.mysunwest.com', 'http://www.novuskin.com', 'http://www.fermeguyon.com', 'http://thecleaningmonkey.com', 'http://www.ultdmotors.com', '1592838466', 'http://cfmphoenix.com', 'http://www.drjamiesbikeclinic.com/', 'https://www.sunsetgrill.ca', None, None, 'http://lashuplounge.com/', None, 'http://www.tropicalsnoaz.com', None, 'http://charlottemosquitoexterminator.com', '1592838501', None, 'https://www.americancampus.com/student-apartments/il/champaign/tower-at-3rd', None, None, '1592838509', None, 'https://www.filibertos.com', None, None, None, 'http://www.redrockmedical.com', None, 'http://www.clarkcountynv.gov/depts/parks/Pages/community-center-west-flamingo.aspx', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://www.drycleanerpittsburgh.com', 'http://www.weberautomotive.com', 'http://www.unmarkedbeautyandwellness.com', '1592838547', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592838552', '1592838555', 'http://www.airdriedogandpony.ca/', 'http://www.korkangranite.com', 'http://petsatpeaceaz.com', 'http://Candlelightstudio.biz', 'http://www.essencedupapier.com/', 'https://www.cueyecare.com', 'http://www.wildwingcafe.com/locations/gastonia-nc', 'http://www.ymcadanecounty.org', 'http://www.peavlerac.com', '1592838579', None, 'http://www.perrydentalsolutions.com', 'http://www.eternalbeautyinstitute.com', None, None, None, 'http://www.TheLaveGallery.com', None, None, None, 'http://boxcarcafe.ca', 'http://wings18.us', 'http://www.fattuesdaytempe.com/', 'http://www.merlenorman.com/', None, 'http://www.onetribe.life', 'http://www.evenstevens.com', 'http://www.northhillsautomall.com', None, None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://valerianoorthodontics.com', 'http://wendys.com/', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', None, None, None, None, 'http://www.anthonyvincenailspa.com', None, 'http://www.427autocollision.com/', 'http://www.butternutridgeapartments.com', None, 'http://www.nvhairstudio.com', 'http://timothyallenjewelers.com', 'http://www.papajohns.com', 'http://www.wearerebol.com', 'http://www.haulinballslv.com', 'http://trattoriadelpiero.com', 'https://droseaz.com', None, 'http://myorangeleaf.com/frozen-yogurt-store/WI/verona/611-hometown-circle?id=431', 'http://bayviewvillagevetclinic.ca/', None, 'http://www.precisionautomobileservice.com', 'https://www.westmadisondental.com', None, 'https://www.aceparking.com', 'http://www.takeyogastudio.com', 'http://truefadesbarbershop.com', None, 'http://www.diamondbackbilliards.com', 'https://www.republicservices.com/locations/arizona/phoenix-trash-pickup-and-recycling?utm_source=yelp.com&utm_medium=referral&utm_campaign=Field_Support_Website&utm_term=raqkoFI4OwZlHOF6sM18OA', None, 'http://www.booksmarttutors.ca', None, '1592838727', 'http://www.ConcreteAccessoriesInc.com', 'http://www.thewrapshoppe.com', 'http://www.zazaespressobar.com', 'http://www.alleghenycounty.us/parks/spfac.aspx', '1592838742', None, None, None, 'https://smiledirectclub.com/smileshops/charlotte-metropolitan/?utm_campaign=yelppaid&utm_medium=cpc&utm_source=yelp&utm_content=Charlotte', 'https://locations.afw.com/az/gilbert/4700-south-power-rd.html', 'http://www.budget.com/', 'http://www.dsw.com', 'https://www.costco.ca/warehouse-locations/nw-calgary-calgary-ab-543.html', 'http://manoratcatlincourt.com/', 'http://clevelandmanagement.com', None, None, 'http://mcgowanautomotiveupholstery.com', 'http://shopchapter2boutique.com/', None, 'https://www.chilis.com', '1592838788', 'http://phoenixtent.com/', 'http://studentunion.unlv.edu', 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=483', None, None, 'http://walteryoga.com', 'http://www.mintindiancuisineaz.com', None, 'https://www.progressive.com/claims/concierge-service/', 'https://brixxpizza.com', None, 'http://www.culvers.com/restaurants/indian-trail-nc-charlotte-hwy', None, 'http://www.mvsvets.com', 'https://www.vintagenv.com', 'http://deadstock.ca/livestock/', None, 'http://www.labcorp.com', 'http://centrikroofingllc.com', 'http://www.longjohnsilvers.com/', 'https://www.goodyear.com/en-US/tire-shop/Phoenix+AZ+85016-6808+US/000121764', '1592838854', '1592838857', None, '1592838864', '1592838868', 'https://www.walgreens.com/locator/walgreens-4949+w+chandler+blvd-chandler-az-85226/id=3531', 'http://www.printwerxaz.com', 'https://www.take5oilchange.com/locations/nc/charlotte-27/', 'http://gentlegroomer.net/index.php', None, 'http://www.theblindpignoda.com', None, None, 'http://www.realitydefense.com', None, None, 'http://renuauto.ca/', 'http://anakarinasbeautysalon.com/salon.html', 'http://www.twoplatesfull.com', None, 'https://binitattoo.com', 'http://www.indiancurry.ca', 'http://www.wingettesaz.com', None, None, 'http://locations.bannerhealth.com/az/peoria/ophthalmology-peoria-az-bamc_00034.html', 'https://www.homedepot.com/l/Cave-Creek/AZ/Phoenix/85022/480?cm_mmc=seo-yelp&', None, None, 'http://funkypetals.com/locations/store/10', 'http://www.tempeaz.gigiscupcakesusa.com/', 'http://www.mysalonsuite.com/las-vegas.html', 'http://www.lasvegasmela.com', None, 'http://charlottedermatologypa.com/', None, 'http://www.azhumane.org/how-you-can-help-the-arizona-humane-society/shop/thrift-stores/', 'http://www.omnidermatology.com', 'https://www.ccpatio.com', 'http://www.dylocksmith.com', None, None, '1592838980', None, 'http://www.thevueonapache.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Calgary-AB-T2A2N7/840052/', 'http://www.pariwar.ca', 'http://www.bk.com', 'https://yourtiresource.com/tires-auto-repair-medina-oh', None, 'http://www.greentechlv.com', 'https://www.statefarm.com/agent/US/OH/Painesville/Kevin-Kilfoyle-M9LYK5PWNAK', None, 'https://www.arrowheaddesertdental.com', None, 'http://www.automallofcu.com', 'http://2shinymobiledetail.com', 'http://www.brighton.com/', None, None, 'http://www.bestairconditioningplumbingrepair.com', 'http://www.crookedskyfarms.com', 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID192', None, 'http://www.azspotrepair.com', '1592839051', 'https://lologifts.com', '1592839058', 'http://www.autonationcollisioncenters.com/viewlocation.cfm?StoreID=77', 'https://northscottsdale.b2rmusic.com', 'http://www.mininorthscottsdale.com', 'http://www.autobell.com/ab_locations/1610-s-providence-rd/', '1592839072', 'http://www.JimmyJohns.com', 'https://www.mydrnow.com', 'http://kcacinc.net', 'http://www.toquelounge.ca', 'https://store.vioc.com/oh/amherst/2285-cooper-foster-park-rd-44001-060028', 'http://www.verizonwireless.com/stores/arizona/phoenix/desert-ridge-203888/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.joinesp.com', None, 'http://www.wingmachine.com', 'https://fabuloushomemadecookies.wordpress.com', 'http://www.health-local.com/clinic/walk-in-clinics/toronto/ontario/primacy-leslieville-medical-centre/', 'http://www.midas.com/phoenix/store.aspx?shopnum=1286&dmanum=684001', '1592839105', 'http://imperialaz.com/', 'http://www.ncdot.org/dmv', 'http://www.ftwbrazilianjiujitsu.com', 'https://www.mattressfirm.com/stores/nc/waxhaw/mattress-stores-waxhaw-nc-28173-6619.html', 'http://www.grabbagreen.com', 'http://www.vapemeet.ca', None, 'http://www.mrshine.com', 'http://www.ctnailsnv.com', None, 'https://perfect-patio.com', 'https://www.jerseymikes.com/9003', None, 'http://www.rawfoodexpress.com/', None, 'http://sellbusinessinlasvegas.com', 'https://genevafi.com', 'http://www.pittsburghdrainguys.com', 'http://stores.maxmuscle.com/nv-las-vegas-1410', 'http://www.marketmall.ca', 'http://stores.sallybeauty.com/az/mesa/beauty-supply-mesa-az-3479.html', None, 'https://www.sgtclean.com', 'https://www.wishentertainmentparties.com', None, '1592839200', '1592839204', 'https://www.luceraapts.com', None, 'https://butterplumbing.com', 'http://www.carolinavw.com', 'https://www.papajohns.com', None, 'http://www.daburgershack.com', 'http://www.viridianpalmsapartments.com', 'https://www.burgerim.com/our-locations/charlotte-2/', 'http://www.raymerfh.com/', 'http://fiveguys.com', None, 'http://www.britanniapub.ca', 'http://scottsdalebellerive.com', 'http://www.azbarkandpurr.com', 'http://www.reddevilrestaurant.com/', None, 'https://www.walmart.ca/en/stores-near-me/westbrook-store-3009', 'http://www.marriott.com/hotels/travel/pitok-courtyard-pittsburgh-shadyside', None, None, 'http://thebitingedge.com', 'http://vprstoronto.com', None, 'https://obgynofakron.com', 'http://www.starbucks.com/store/9229/', 'http://www.gamestop.com', None, None, 'http://www.centurycycles.com', 'https://www.animalcareclinicinc.com/stephanie-animal-hospital', 'https://facialsbydania.wixsite.com/mysite', 'http://cococochocolatiers.com', None, 'https://locations.massageenvy.com/illinois/savoy/1213-savoy-plaza-lane-suite-d.html', None, None, None, 'http://www.communicarehealth.com/facility/copley-health-center', 'http://thehauntedmuseum.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.shanksplumbing.com/', 'http://www.lolihairstudio.com/', None, None, None, 'https://www.thecapitalgrille.com/locations/nc/charlotte/charlotte/8011?cmpid=br:tcg_ag:ie_ch:dry_ca:TCGQ420LOCURL_dt:20200520_sn:yelp_gt:charlotte-nc-8011_pl:locurl_rd:1008', None, None, 'http://charlottebikes.net', 'http://www.spirithalloween.com', 'http://www.veteranautoglass.com', 'http://sixtree.ca', None, None, 'http://www.eliteappliancesrepair.com', 'https://www.umcsn.com/Quick-Cares/Quick-Care-Locations-Nellis.aspx?intMenuID=112&intPageID=193', 'http://www.hamptonhampton.com', 'http://www.fantasticsams.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, None, None, 'http://www.enhancedentallv.com', 'http://www.sbarro.com', 'http://www.rainbowcafeuptown.com', None, 'http://www.lowes.com', None, 'https://azdirect.az.gov/economic-security', 'http://www.deltaco.com', 'http://www.atsaz.net', None, 'http://restaurantchezkhady.com', 'http://www.tablesbgs.com', 'http://www.athletescare.com', None, None, None, 'https://www.millenniumlocksmith.com', 'http://seacretnailandspa.com', 'https://www.honorhealth.com/locations/specialty-care/breast-health-and-research-center-deer-valley?utm_source=yelp&utm_medium=local&utm_campaign=Breast_Health_And_Research_Center_Deer_Valley', 'https://www.nike.com/us/en_us/retail/en/nike-scottsdale', 'https://locations.visionworks.com/ll/US/PA/Pittsburgh/120-Fifth-Ave-Pl', 'https://www.charlotteplasticsurgery.com/our-practice/dr-jack-f-scheuer/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://thecrateescapepgh.com', None, 'http://www.justyoulv.com', 'http://www.fox10phoenix.com', None, 'http://www.tattoo-noir.com', None, None, 'http://www.tint-360.com', None, 'http://www.chevys.com/', 'http://thestudioslv.com', 'http://heywoodmanagement.com', 'http://www.quiktrip.com', 'https://www.massagetherapymadison.com', None, 'https://sazeracphoenix.com', None, '1592839598', 'https://www.storage-mart.com/toronto/north-york/arrow-road?utm_campaign=yelp_paid&utm_source=yelp&utm_medium=paid&utm_content=3024', 'http://mightymangorestaurant.com', 'http://www.associans.com', 'http://www.coachandhorsescalgary.com', 'http://www.carysauto.com', None, 'http://www.spicypickle.com/', 'http://www.arizonabiltmore.com/dining/frank-and-alberts/', 'http://www.alterationstailoringservices.com', 'http://www.td.com', 'http://www.bbvsalon.com', 'http://www.astepaheadpreschool.com', 'http://www.mafiamikespizza.com/', None, 'http://www.precoll.net/', None, 'http://www.gmtcare.com', 'https://vo5nailsspamesa.com', 'http://www.dollartree.com', 'http://www.dollarama.com/', 'https://www.pghchiroassociates.com', 'http://arizonawomenscare.com', 'http://quickpickk.com', None, 'https://www.galaxytheatres.com/Browsing/Cinemas/Compare?Cinemas=6', 'https://legendsonthestrip.business.site', 'http://www.valleygardencenterphx.org', 'https://www.simonmed.com/locations/all/simonmed_imaging___deer_valley', 'www.puresushibar.com', 'https://www.elitenutritionlv.com', None, 'https://locator.chase.com/az/fountain-hills/16744-e-ave-of-the-fountains?jp_cmp=rb/LocalListings/aff/branch/na', None, None, 'https://albertossportsbarandgrill.com', 'http://www.AvantePrintCenter.com', 'http://www.bsidebistro.com/', None, 'http://www.homelovers.com', None, 'https://swiftservicemen.com', 'http://exclamationssalon.com', 'http://artistic-arborist.com', None, 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', None, 'http://www.salsbarbers.com', None, 'http://www.irenescelebritycakes.ca', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, 'http://www.discountgolfcarsofaz.com', 'http://www.makeovermygaragedoor.com', 'http://www.reesors.ca', 'https://www.lgcollisioncenter.com', 'http://www.hirts.com', None, 'http://www.ohboyburger.com', 'http://www.mvpkidscare.com', 'http://www.greencabofcharlottenc.com/', None, None, 'http://www.belmontdentistry.com/', 'http://topautomotiveinc.com', 'http://HendersonPavilion.com', '1592839838', 'http://millerandsonssupermarket.com/MHmillers.aspx', None, 'http://tomfridaysmarketpa.com', 'http://www.hubbardavenuediner.com', 'http://www.pitgranite.com/', None, 'http://www.consignmentsonpark.com/', '1592839863', None, None, None, 'https://isabelles-kitchen-mexican-food.business.site', 'http://www.svdpmadison.org/shop/waunakee', None, None, None, 'http://dogsrulegrooming.com', 'https://www.reginaldscoffee.com', 'http://ailcareers.com', 'http://www.lowes.com', 'http://www.reevescollege.ca', 'http://www.nirvanathruyoga.com', 'http://www.redlinealarmcompany.com/', 'http://lasvegasfoodiefest.com/', 'http://www.coffeebean.com', 'https://www.garagedoorservice.com/kansas-city/independence', 'http://monogramcoffee.com', None, 'http://www.themintaz.com', None, 'http://usbphoneworld.com', 'http://www.KonaSnowballs.com', 'http://robertostacoshop.com', None, None, 'http://www.jimmythegreekgroup.ca', None, 'http://hollywoodnails4u.wix.com/home', None, 'http://www.trufusionscottsdale.com', 'https://www.sprouts.com/stores/details/-/store-details/view/store/13/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.apria.com', 'http://www.simitandchai.co', None, 'http://www.depasquachiropractic.com', 'http://www.phxinjurylaw.com', '1592840005', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://ranchotireslv.net', 'http://bestinpets.net', 'http://www.chapters.indigo.ca', 'http://www.frocks.ca', 'http://www.sincityclubcrawl.com/', 'http://www.carmonsrestaurant.com/', None, 'http://www.portofsubs.com', None, None, None, 'https://agents.allstate.com/kevin-lum-chandler-az.html', None, None, 'http://Www.selfmadetrainingfacility.com', 'http://www.humptys.com/', 'http://www.azmetrohauling.com', 'http://kechusa.com', 'http://www.greatclips.com', 'http://www.popeyeschicken.ca', None, 'http://www.thewritersblock.org', 'http://www.dontbebroke.com/?utm_source=Yelp&utm_medium=Location%2BPage&utm_campaign=Yelp', None, 'http://www.vegashomesre.com', 'http://www.phillipsdisability.com', 'http://weareallwrestlers.com', 'http://www.starbucks.com/store/8167/', 'http://www.shaghairsalon.biz/', 'http://www.dunkindonuts.com', 'http://www.joujouhairstudio.com/', 'http://www.christophermoving.com', None, None, None, 'http://www.torontohonda.com', 'http://www.rockstarbootcamp.net/', 'http://www.shawarmarama.ca', 'http://regissalons.com/salondetail/default.asp?salonid=27089', 'https://www.sarahnicolehair.com', 'http://divadivineboutique.com', 'http://www.paksweets.com', 'http://www.costcutters.com/', None, None, None, 'http://www.7-eleven.com/?yelp=35583', None, 'http://www.eurodeliandbakery.ca', 'http://www.artonwheels.tours', 'http://www.billysacappellimartinibar.com/', 'http://wilsongarageakron.com', None, None, 'http://goldennationalcalgary.ca', None, 'http://www.bavariasausage.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://sobas.com', 'http://dnailandspa.wix.com/d-nail-salon-spa', None, None, 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpsouthwestorganic', None, None, None, 'http://destinyasianfusion.com', 'http://www.dunkindonuts.com', 'https://www.aspendental.com/dentist/oh/mentor/7610-mentor-avenue?utm_source=YP&utm_medium=IYP&utm_campaign=Mentor,OH-MMIYP%7C%7CMentor_OH%7C%7C6372&office=6372', 'http://www.phoenixstorks.com', 'http://carmencarmensalon.com', None, 'http://www.vampdvegas.com/', 'http://www.canyonanimalhospitalphoenix.com/', 'http://www.drkenhogan.com', 'https://www.starbucks.ca', 'http://carolinawoodflooring.com', '1592840282', None, 'http://www.quiznos.com', 'http://www.2ndnaturebakery.com', 'http://scottsdalebible.com', None, 'http://www.hillcresthawks.com/', None, None, 'https://urbanoptique.ca', '1592840312', None, 'http://www.mamaspizzaexpress.com', '1592840324', 'https://www.mecknc.gov/ParkandRec/Parks/ParksByRegion/NorthRegion/Pages/ShuffletownPark.aspx', '1592840329', 'https://parma.onyxhealthclub.com', None, 'http://azmassagepro.com', 'http://www.neurotica.ca', 'http://www.madisonsmoothmoves.com', None, None, 'http://www.eyemartexpress.com/get-glasses/Champaign/61822', 'http://www.prankstersgarandbrill.com', None, None, 'http://www.brampton.ca/EN/residents/Community-Centres/Chinguacousy-Wellness-Centre/Pages/Welcome.aspx', None, 'http://www.mylittlepizzeria.com', 'https://www.jerseymikes.com/3081', 'http://www.lonewolftradingco.net', None, 'http://www.thegrovecafeaz.com', 'http://www.culinarium.ca', 'https://greeneffecttree.com', None, 'http://www.SportRentals.ca', 'http://www.finereflectionssalon.com/', 'http://www.i-technique.ca', 'http://www.snvls.com', 'http://counselmortgagegroup.com', 'http://www.livewithcapstone.com', None, 'http://www.theburnhamrestaurant.com', 'http://www.ctrplumbing.com/', 'http://www.noiretoile.com', None, '1592840445', 'https://www.freeport-logistics.com', 'https://www.sendingloveroses.com', 'https://www.wilhelmyflorist.com/?srccode=yelp_track', None, None, 'https://www.hometrust.ca', 'http://www.davisfuneralservices.com', 'http://www.sugarhappyaz.com', 'http://ourtownsrestore.org', 'https://www.islandschiro.com', None, None, 'http://www.TheMirrorMirrorSalon.com', 'http://www.itsallgoodbbqandmore.com', 'http://www.pompstire.com/', 'https://www.azbuslaw.com', None, None, 'http://www.madison-massage.com/Home.html', 'https://Genteks.net', 'https://www.mrrooter.ca/calgary', None, 'http://www.25eventmanagement.com', 'http://www.saloncarmens.ca/', 'http://www.yeagerchiropractic.com', 'http://cuyahogalibrary.org/', 'http://downtownwineryto.com', 'http://newyorknewyorkbodypiercing.com/', None, 'http://www.LowesAV.com', None, None, 'http://www.salonhills.com', 'http://jayarrcustoms.com/', 'http://matchateadessert.ca', 'http://www.allensspa.com/', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', 'https://www.walmart.com/store/4336/el-mirage-az/whats-new', 'https://www.seniorhelpers.com/az/scottsdale', 'http://www.dunnsimport.com', 'http://www.seoulmarketaz.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.theartofbraces.com', None, 'http://galleriapediatricdentistry.com', None, 'http://www.brocktquinn.com?cmpid=dk16_blm_0006', None, None, 'http://goldscissorsbarber.com', '1592840609', '1592840613', 'http://empireroofingandmore.com', None, None, None, 'http://www.captureyourlifeinpictures.com', 'http://reviveaz.com', None, 'http://drreidhead.com', 'https://www.servpronorthwestcharlottenc.com', 'http://www.drhuclinic.com', None, None, 'https://stores.petco.com/oh/macedonia/pet-supplies-macedonia-oh-1958.html', 'https://www.escaparium.ca/montreal-escape-game/contact/', 'http://www.tracyessiglaw.com/', None, 'http://www.stillsmokinglv.com', None, None, 'http://www.ko-chi.org', 'https://www.carquest.com/stores/nv/las-vegas/14974', None, 'http://www.liquidationbureau.com', None, 'http://cutsncurls.net', None, 'http://raptordigitalmarketing.com', None, 'http://www.giuseppezanottidesign.com/us', 'http://www.winduprestaurant.ca/', 'http://www.anddogstoo.com/', 'http://cityoven.com/', 'http://www.rebdlv.com', None, 'http://www.atlasdentallv.com', 'https://www.millenniumhotels.com/en/scottsdale/the-mccormick-scottsdale/', 'http://www.tattoo-pittsburgh.com/', 'https://www.rowcustompools.com', None, None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.jcrkelly.com', 'http://www.cccnevada.com/doctor/margaret-terhar-md-facs/', None, None, 'http://www.hatclub.com', None, None, 'http://www.proofcanteen.com', 'http://bikevaletaz.com', 'http://www.bakerykaffeehaus.com', 'http://made2measureclothing.com/', 'http://www.tallmadgegoldenplace.com', 'http://insurance-agency.amfam.com/IN/jerry-wheeler/default.aspx?sourceid=agp0001014258', 'http://chickenbonz.com', None, 'http://www.infinitemedicalweightloss.com', None, 'http://www.bluegrottopizza.com', None, 'http://www.baumbickchiropractic.com', None, None, 'https://local.albertsons.com/az/gilbert/861-e-warner-rd.html', None, None, 'http://www.fantasticsams.com', 'http://www.applebeescanada.com/restaurants/information/calgary-sunridge', None, 'http://www.brennanscolony.com/', 'http://www.fiestafilipinacuisine.net', 'http://www.bleugourmet.com', 'http://www.themainstreettattoo.com', None, 'https://www.steaknshake.com/locations/az-tempe-s-mill-avenue', 'http://www.swisschalet.com', None, 'http://www.jewishharrisburg.org', 'http://123appliancerepair.com', '1592840912', 'http://www.topvegasbuyer.com', 'http://www.rockstarlandscape.com', None, 'http://punjabibynature.ca/home.html', 'https://www.kfc.ca//store/415-mount-pleasant-rd-toronto', 'http://www.cpk.com/location/details/Fashion-Show-Mall', 'http://www.discounttire.com', 'http://www.magnusonhotels.com/Magnuson-Grand-Hotel-Madison', 'https://www.dairyqueen.com/ca-fr/Locator/Detail/?store-id=1990&localechange=1', 'https://www.FireProtectionPhoenix.com', 'http://www.mcvsalon.com', None, 'http://www.strengthcenterlv.com', 'http://www.zigzagzoo.ca', 'http://thewingfactory.ca', 'https://oralecmc.com', 'http://www.advancedmanualtherapy.com', '1592840979', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.AllVegasAutoGlass.com', None, 'http://www.vegaspaintingparties.com', None, 'https://www.marketdistrict.com/store-locator/store-details?number=1611', None, 'https://www.carillonassistedliving.com/our-communities/huntersville/', 'https://www.bobevans.com/our-restaurants/locations/584?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'https://experimax.com/locations/edgewood-pa/?utm_campaign=yelp_ads&client=8014-80167&utm_medium=CPC&campid=20&utm_source=yelp', 'http://johnwooddds.com', None, 'https://fixautousa.com/el-mirage', 'http://www.novelsweets.com/', 'http://www.maditalian.ca', 'https://www.bluedotdental.com', 'http://www.teasnow.com', '1592841044', 'http://cozyinnpetresort.net', None, '1592841052', None, None, 'http://www.timhortons.com/', 'http://www.pooperpickerupperkids.com', None, None, None, 'http://pizza.dominos.ca/Mississauga-Ontario-10348', None, 'https://www.wyndhamhotels.com/hotel/46513?tel=18882935571&iata=00093785&cid=fe:bh:20161215:yl:pp:hawus:46513', 'http://www.charmingcharlie.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://bigwatempe.com', None, 'http://www.sorsiemorsi.ca', 'http://www.mozaikskin.com/', None, 'http://www.victorybmw.com', 'http://www.peninsulabistro.com', 'http://boydslobstershop.ca', 'http://www.thecupcakeshoppe.ca/welcome.htm', 'https://www.helmuttspetsupply.ca', 'https://www.wildwingrestaurants.com', 'http://msmacncheese.com', 'http://www.areadisposal.com', None, '1592841134', 'http://www.burningrivertattoos.com', None, 'http://www.thecamerastore.com', None, None, 'https://agents.farmers.com/az/scottsdale/joseph-fritz?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.carmelfoot.com', 'http://fareasttaco.com', 'https://www.sunnyjimstavern.com', 'https://bellabridesmaids.com/pages/bella-bridesmaids-charlotte', 'https://vitalizemedspa.com', None, 'http://predatorsreptile.com', None, 'https://www.labcorp.com', 'http://www.salonorozco.com', 'http://willeauto.com/', None, 'http://www.myiPhoneDoctor.com', 'http://www.lululemon.com/pittsburgh/shadyside?cid=yelp', 'http://www.burntwoodtavern.com', '1592841215', 'http://thebutterjoint.com', None, None, 'http://www.everythingbutwater.com', None, 'http://www.allaboutimports.com', 'http://smokespoutinerie.com', None, 'http://www.azfoundationworks.com', '1592841251', 'http://www.bonfoey.com', 'http://www.games-workshop.com', 'http://eathealthyeatgreek.com/locations/paradise-valley/', None, 'http://bjsautospa.com/', None, 'http://www.desertwestsurgery.com', 'http://www.switchtoronto.com', None, 'https://www.opalonpearl.com', 'http://www.skoah.com', 'http://www.lvlashbar.com', 'https://www.spauldingstreeservice.com', 'http://www.aldi.com', 'http://www.bestvibes.ca', None, 'http://www.parkviewniteclub.com/', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_500', 'http://www.medcan.com', 'http://www.moonvalleycc.com', 'http://702dads.com', 'http://brightsuncleaning.com', 'http://www.livemillennium.com/profile.asp?AID=13450', None, 'http://blgwins.com', 'http://www.thecopa.ca/#!vaughan/cr38', '1592841336', None, 'http://mentorlumber.com/', None, 'http://www.classicmaids.ca/', 'http://www.turnstyleconsign.com/arizona/mesagilbert/', 'https://plan.dignitymemorial.com/yp/plan/?id=480111050&utm_source=yp.com&utm_campaign=ypm&utm_medium=display&utm_term=399&utm_content=mlp', 'https://chatters.ca', None, 'http://www.sunstonerestoration.com/', 'http://www.macks-auto.com', 'https://www.amctheatres.com/movie-theatres/charlotte/amc-concord-mills-24?utm_uid=yelp', 'https://www.nvpcfix.com', None, None, None, 'http://caffedaniel.com/', 'http://asyouwishpottery.com', None, None, 'https://www.unleashednc.com', 'http://celebritytanning.com', 'https://www.theplatinumhotel.com/restaurant-bar-vegas/stir-lounge', None, None, 'http://www.vcahospitals.com/heritage/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Heritage_Animal_Hospital&utm_campaign=main_url', None, None, 'http://atvrentalsscottsdalearizona.com', 'http://unitylasvegas.com/', 'http://www.toysrus.com', 'http://DesignsbyKelleyLayne.com', 'http://www.coach.com', 'http://www.UnderstandingOurDogs.com', None, 'http://www.burlingtoncoatfactory.com/store-details-Store-156--4000-Oxford-Drive--Bethel-Park--PA--15102-1840.aspx?from=15102&id=8cdd1753-86f2-4fe5-a3ad-a986545c6e4b', 'http://www.bakerysocial.com', 'https://lakelasvegaswatersports.com/rentals/', 'http://hotstonegrillnc.com', None, 'http://www.wagsnkisses.com/', None, 'http://www.crossfitcleveland.com', 'https://personaleyeslasvegas.com', 'http://www.garvinpromo.com', 'http://refinemenssalon.com/chandler-ocotillo/', 'https://www.joefresh.com/ca/', 'http://www.carolynnreynolds.com', 'https://yoasis.business.site', 'http://www.olivastrooils.com', None, 'https://www.bbvacompass.com/USA/AZ/Glendale/5740-W-Bell-Rd/', 'http://www.venturamarket.com', None, 'http://www.tdscustomconstruction.com', 'http://www.superiormotors15104.com/', None, 'http://http.www.mentorsaltcave.com', None, 'http://galleriesguadalajara.com/', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', None, 'https://local.biglots.com/az/surprise/4504?zcp=pd_local_yelp', 'https://www.scottsdaleaz.gov/parks/dog-parks', None, None, 'https://allurecharlotte.com', 'http://www.bojangles.com', 'http://www.audinorthscottsdale.com/index.htm', None, None, None, 'http://www.maccosmetics.com', '1592845037', 'http://queenofsoups.com', 'http://www.beauticiansonthego.com', 'http://www.gong-cha.ca', 'http://order.papajohns.com/', 'https://www.petsmart.ca/stores/ca/on/east-york-store0935.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', 'http://www.ortensiaspa.com', 'http://www.purplerainpolefitness.com', 'http://www.starbucks.com', 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, 'http://www.papajohns.ca', None, None, 'http://medpost.com/location/gilbert-az', 'http://www.calatlantichomes.com', None, 'http://www.your-anchor.com', None, 'http://www.RentingSeasons.com', '1592845116', None, 'https://www.budget.com/budgetWeb/locationsearch/details.ex?pul=CLT&selected=0&checkDolStatus=false&checkPulStatus=false', 'http://www.batcavecomic.com', None, 'https://www.buildingarizonafamilies.com', 'http://www.atccafe.com/', 'https://theolivemerchant.com', None, 'http://www.kidtokid.com', None, None, 'https://locations.theupsstore.com/ny/hudson/160-fairview-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.torontoairportslimousine.com/', 'http://www.empirephotos.com/', None, 'http://homewoodsuites3.hilton.com/en/hotels/alberta/homewood-suites-by-hilton-calgary-downtown-YYCDWHW/index.html?SEO_id=YELP-HW-YYCDWHW', 'http://www.rinaldisdeli.com', 'http://mosharrafa.com', None, None, 'http://samadhiteahouse.com', None, None, 'http://www.baskinrobbins.com', 'http://www.cigarbodega.com/cigars.htm', 'http://times3sportsgrille.com', None, 'http://kidsdentalgroup.ca', None, 'https://dominicspizzeria.business.site', 'http://www.t-mobile.com', None, '1592845219', None, 'http://thebagelstop.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.como-pizzeria.com', 'http://www.cityvetsairdrie.com', 'http://www.pawn-az.com', 'http://www.valleyheart.us', None, 'http://www.clevelandheatinginstallation.com', 'http://mattygs-az.com', 'http://www.computerdeli.com', 'http://www.wackynackies.com', 'https://www.wellsfargo.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.ontariosciencecentre.ca/', 'http://www.harveys.ca', 'http://kanplumbandhandymanservices.com', 'http://www.maillinkplus.com', 'http://mod-n-art.blogspot.com', 'http://cookinguptown.com/', 'https://westhillsveterinaryclinic.com', 'https://www.olivegarden.com/locations/la/monroe/monroe-la/4488?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:monroe-la-4488_pl:locurl_rd:1818', 'https://www.therange702.com', 'http://www.NikkiBsellsAZ.com', None, 'http://www.burnschevycadillac.com/?cs:pro=repman&cs:e=yelp', 'http://www.fancyfootspa.com', None, 'https://www.chucksroadhouse.com', 'http://www.bobssub.com', 'http://www.allohiomotorsports.com', 'http://www.gardentuscana.com', None, 'http://www.atomic.vegas', 'http://www.smilesolutionsdentist.com/', 'http://www.sincityscuba.com', '1592845318', None, 'http://local.fedex.com/az/phoenix/PHXE/', None, None, 'https://www.ashfordgreenapts.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.diamondsbeautybar.com', 'https://ashleyhomestore.ca/pages/mississauga', 'http://sidewalkpizzeria.com', 'http://www.activebodies.net', 'http://www.bathandbodyworks.com', None, 'http://www.binghamequipment.com', 'http://www.toyotekaz.com', 'https://pizza.dominos.com/north-carolina/mount-holly/553-s-main-st/', None, 'http://www.WolfandLambLV.com', 'http://riverviewgolfcourse.com', None, 'http://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLECW', 'http://bigshotbobs.com', 'http://www.uacqb.com', 'https://locations.levi.com/on/mississauga/denim_mississauga_on_ca104.html', 'http://www.cbsortho.com/', None, 'https://rakutensl.com', 'http://www.leftseatrestaurant.com', '1592845394', None, '1592845397', 'http://www.themandrakeclt.com', 'http://www.nvfire.com', 'http://www.diamondsintheruffpetgrooming.com', 'https://www.brakesplus.com', None, 'http://www.hertz.com', 'https://clipper-doodles.business.site', None, None, 'https://www.redlobster.com/locations/list/oh/cuyahoga-falls/1090-graham-road', 'http://www.aglowingsmile.com', 'http://www.neatspace.ca/', 'http://www.godarusa.com', None, 'http://www.govbergwatches.com', None, 'http://ruffhousinglv.com', 'http://www.clevelandymca.org/north-royalton.html', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.swjbuyers.com', 'https://www.sprouts.com/stores/details/-/store-details/view/store/3/?utm_source=yelp&utm_medium=listing&utm_campaign=website', None, 'http://www.jadenail.ca/', None, None, 'http://www.dunkindonuts.com', 'https://www.hooters.com/locations/nv/henderson/s-eastern-ave/', 'http://malloymemorial.com', None, 'http://www.timothys.ca', 'http://www.mobilemechanicsoflasvegas.com/', None, 'https://locations.massageenvy.com/north-carolina/charlotte/12840-walker-branch-dr.html', 'http://www.BillMerrenLoans.com', None, 'https://revmma.com', 'http://www.charlotterootcanalcenter.com', 'https://www.cosmopolitanlasvegas.com/entertainment/calendar?utm_source=yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.theinkwelltattoocompany.com', 'http://www.dr-diesel.com', '1592845505', None, 'http://www.grillies.ca', None, 'http://www.bitebar.ca/', 'http://www.gofavorco.com', None, 'http://www.phxrisingfc.com', 'http://theguitardog.com', None, 'http://foxandhound.com', None, None, '1592845536', 'http://www.markhaminfiniti.com/', 'http://www.idealbridalaz.com', 'http://www.foxyphotographylv.com', 'http://www.graeters.com/retail-stores/cleveland/crocker-park', 'http://jtownbythesea.ca', 'https://www.bathandbodyworks.com', 'http://www.azfloodsquad.com', 'http://www.marcanthony.com', 'http://cheeseburgernation.com/locations/cheeseburger-las-vegas/', 'http://www.ricospgh.com', 'http://www.chevronwithtechron.com', None, None, 'http://churchschicken.ca', 'http://www.savutimetitles.com', 'https://phoenixpsychic.wordpress.com', None, 'http://www.GoodyHouse.com', 'https://www.aria.com', None, None, 'http://buckstavernlasvegas.com/', 'http://www.bakerstowingandrepair.com', None, 'http://www.crazybee.ca', 'https://www.calgarycoop.com', '1592845607', 'http://www.trendautorepair.com/', 'http://www.iautonc.com', 'https://mrtokyojapanese.com/manroe/', None, 'https://www.suncoastcasino.com/dine/casual-dining/briggs-oyster-co', 'https://www.fortmillhyundai.com/?utm_source=yelp&utm_medium=business_url&utm_campaign=local-citations', 'http://www.waxpert.ca', 'http://www.Eartique.com', 'http://www.bonannosnewyorkpizzeria.com/menu/flamingo-food-court/', 'https://www.thebiggreenk.com/locations/uptown/', '1592845637', 'http://www.fatherandsondentistry.com', None, None, 'https://www.presscoffee.com', 'https://www.nike.com/retail/s/nike-factory-store-las-vegas-north', 'http://www.hopfarmbrewingco.com', 'http://www.pudgieseatery.com', None, 'https://www.walmart.com/store/3250/aurora-oh/details', None, None, 'http://luxurythaispa.com', None, 'https://locations.captainds.com/ll/US/NC/Gastonia/360-N-New-Hope-Rd', 'http://www.chiemiphotography.com', '1592845675', 'http://freshlandsupermarket.ca', '1592845681', 'http://beefandbottle.net', 'http://www.copleychiropracticclinic.com', None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.lubbencounseling.com', None, 'http://www.chezcora.com/fr/restaurants/quebec/Cora-Vimont-Laval', None, 'http://www.summerlink.com/recreation-and-parks/parks-and-amenities/parks#centre', 'http://www.z-cafe.net/', 'https://www.famousfootwear.com/?partnerid=YELP', 'https://www.bannerhealth.com/locations/tempe/banner-urgent-care-1', None, 'http://www.charlottebartendersball.com', None, '1592845715', 'https://redrock.sclv.com/?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', 'http://www.alexandani.com/miracle-mile', 'http://www.ampm.com', 'http://www.novelistaz.com', '1592845728', 'http://www.alliedflooringservices.com', None, 'http://barrickmuseum.unlv.edu', None, 'http://www.charlotterusse.com/', None, 'http://www.chinarose.ca', 'http://www.fromageriedesnations.com', 'http://702locksmithlv.com', None, 'http://phoenix-weightloss.com', 'http://www.paulrenefurniture.com', 'http://www.bojangles.com', 'http://www.bridgeville-paws-n-claws.com', 'https://www.wastedgrain.com', None, 'http://www.contourslingerie.com', None, 'http://www.costco.com/warehouse-locations/centennial-las-vegas-nv-737.html', 'http://spectrumwellnessaz.com', 'http://www.flipnoutxtreme.com', 'https://www.servprodowntownlasvegas.com', 'http://mirrasplace.com', 'http://www.phoenixautoglassrepair.net', 'http://www.feetmd.com', '1592845789', None, 'http://valleymetro.org', 'http://www.windypawn.com', None, 'http://www.beaconhillstaffing.com', '1592845806', None, 'http://www.nps.gov/dabe/index.htm', 'http://www.compasschurchaz.com', 'https://www.gingiespa.com', 'http://rossispizzamonona.com/', 'https://www.redhillbrewing.com', 'http://www.clearwire.com', 'http://popeyeschicken.ca/', 'http://labellenailspalasvegas.com/', None, 'http://invisioneyecareaz.com', 'http://www.johnsplacematthews.com', '1592845844', 'http://www.taylorscafe.com/scottsdale', 'http://www.williams-sonoma.ca', None, None, None, 'http://www.eatmorefellinis.com', None, 'http://www.starbucks.com/store/9298/', 'http://www.thetikihideaway.com/', '1592845871', None, None, 'http://www.pilatesjoe.com', None, None, 'http://expertairconditioningandheating.com', '1592845891', 'http://www.thepaintedlady.ca', None, 'http://www.alturaontropicana.com', None, None, 'https://stores.bestbuy.com/az/phoenix/2440-w-happy-valley-rd-1481.html/?loc=ns100&ref=NS', 'http://www.floridaflowers.ca/', 'http://www.renue.ca', 'http://www.clarkcountynv.gov/', 'http://www.fitness-nw.com', None, 'https://www.bugsysblinds.com', 'http://www.jurassicgrill.com', None, 'http://www.3-monkeys-eatery.com/', '1592845947', 'https://www.runningroom.com/hm/inside.php?id=2488', None, 'https://www.staples.com', None, None, None, 'https://www.lifestorage.com/storage-units/ohio/cleveland/44060/121-in-mentor/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-OH-121&utm_content=website-link&howheard=IYE', None, 'http://www.orkin.com/locations/branches/?zip=85233', None, 'https://yobahut.com', 'http://www.oneguardhomewarranty.com/', 'http://walmart.com/', 'http://heiserheating.com', None, 'http://tocayaorganica.com', 'http://www.sheenagalphotography.com', None, 'http://www.chinaseaoh.com', 'http://brownssocialhouse.com/chestermere', 'http://www.pizzapizza.ca', 'http://www.summitsocietyphx.com', None, '1592846040', 'http://www.chamecha.com/', None, None, 'https://www.bose.com', 'http://www.creeds.com', None, None, 'https://nothingbundtcakes.com/bakery/NC/concord?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=concord_258', 'http://www.midtownflatsphoenix.com', 'http://www.rajbhog.com/index.php?store_id=11&file=storelocations-detail', 'http://www.yogamcc.com/', 'http://www.vitalposture.com', 'http://locations.smartandfinal.com/az/tempe/480/', 'https://ad.doubleclick.net/ddm/clk/434423347;236814625;g', 'http://www.luxebeautysalon.biz', 'http://www.20loungekierland.com/', 'https://www.storagewest.com/facilities/buffalo-drive/?utm_medium=organic&utm_campaign=yext&utm_source=yelp', 'http://www.jangwontoronto.com', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.CircuitFitnessLv.com', 'http://mckenziewellness.com', 'http://www.topiarysrestaurant.com/', 'http://www.massage-synergy.abmp.com', 'http://www.sicilianristorante.com', 'https://www.chick-fil-a.com/rossparkmall', 'http://www.shislerscheesehouse.com/', None, 'http://projectmanagementacademy.net/pittsburgh/pmp-certification.php', None, 'http://www.marcellasscottsdale.com', 'http://www.fuzziwigscandyfactory.com', None, 'https://www.pellabranch.com/yelp', 'http://16sttiresandservice.pro', 'https://www.cellairis.com/store-locator', 'http://1800taxicabcleveland.com', 'http://www.timhortons.com/', None, 'https://sandownmarket.com', 'http://www.neimanmarcus.com/store/info/store.jhtml?storeId=15/LV', None, None, 'http://www.lcbo.com', None, 'http://prompttitles.net', 'https://www.merriammusic.com/studio/', 'http://www.paradiseislandbowl.com/', None, None, 'http://www.auntieannes.com', 'http://duncancomics.com', None, 'http://www.stvincentdepaul.net', 'http://www.tenichicuisine.com', 'http://ramproline.com', '1592846227', 'http://www.wincofoods.com', 'http://www.aokpeds.com', 'http://tonyhecht.com', 'http://www.s2bride.com', None, None, 'http://colombianperuvianfoodmesa.com', 'https://locations.theupsstore.com/az/phoenix/4802-e-ray-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://www.lafiestagrandenc.com', None, 'http://www.atcoblueflamekitchen.com', 'http://www.straightarrowroofing.com', 'http://www.edbozarthlasvegas.com', 'http://www.dreamnightlimousine.ca', 'http://www.availvapor.com', None, None, 'http://storelocator.pepboys.com/pepboys/stores/phoenix/cactus/00747', 'http://www.meattheball.com', 'https://locations.riteaid.com/locations/pa/bethel-park/5100-library-road.html', None, 'http://danrandandassoc.com', 'http://www.newbalance.com/on/demandware.store/Sites-newbalance_us-Site/default/Stores-Find', 'https://www.definedcoffee.com', None, 'http://www.manpower.ca', None, 'https://parkermedical.org', None, 'http://www.xshowslasvegas.com', None, 'http://www.jade-dragon-charlotte.com', 'http://www.embroiderystorevegas.com', None, None, None, None, 'https://www.petsuppliesplus.com/Store/OH/Chardon/Chardon/119?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'https://www.harveys.ca', 'http://www.brighteyesvegas.com', 'http://www.dsw.com', 'http://www.timhortons.com/', 'http://www.jordans.ca/store-locations/calgary-location/', None, 'http://www.eloquenttimesphotography.com', 'http://www.ahome4spot.com', None, 'http://www.cbpremiumautos.net', 'http://www.foxandfiddle.com', 'http://www.gerrickscustom.com/', 'https://www.loudrumor.com', 'http://www.mymacs.ca/macs-stores/ca/calgary/2000-airport-road-ne/22172', 'http://www.deserthandtherapy.com', 'https://www.hardees.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, 'https://www.pthealth.ca/clinic/corporate-sport/?ibp-adgroup=yelp&utm_campaign=premium-listing&utm_source=yelp&utm_medium=directory', 'http://goinpostal.com/', 'https://www.aligndoula.com', None, 'http://www.biltmoredomicile.com/', 'https://business.google.com/website_shared/launch_bw.html?f=vegas-noodle-house.business.site', 'http://www.choicehotels.ca', 'http://fischerinstitute.com/', '1592846457', '1592846462', None, 'http://www.pittsburghpetfence.com', None, 'http://stores.sallybeauty.com/az/mesa/beauty-supply-mesa-az-3479.html', 'http://www.benbridge.com', None, 'http://symposiumcafe.com/thornhillrestaurants.html', 'http://www.viva-raw.com', 'http://www.waterfrontoronto.ca/', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.wendys.com/', 'http://www.sno-ballmania.com', '1592846522', 'http://www.papajohns.com', None, 'http://www.joerockheads.com', None, None, 'https://www.gerbercollision.com/locations/glendale-az', None, 'http://www.apple.com/retail/santanvillage/', None, None, None, 'https://www.thejoint.com/wisconsin/fitchburg/fitchburg-30003', '1592846571', 'http://www.littlecaesars.ca', 'http://www.mommyrents.com/', None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7784&localechange=1', 'http://artsjunkremoval.com', '1592846596', None, 'http://www.shadowtinting.com', 'http://www.prestigecleaners.com', None, None, 'http://www.kelseys.ca/', 'http://www.lotusinn.ca/', None, 'http://www.tirekingdom.com', None, '1592846646', None, None, 'http://www.reformedpilates.com', 'http://www.greenmango.ca', None, 'http://www.shivaga.com', 'http://www.firkinpubs.com/thebullandfirkin/', 'http://www.cuttingedgehairetc.com', 'http://www.sharksseafooddeli.com', 'https://thepetclub.com', 'http://www.pho99.com/', None, 'http://www.amaezing.net', 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', 'http://www.beautyone1.com/', 'http://southeuclidpawn.com/', 'http://glhc.abmp.com', 'http://www.streetsofnewyork.com', 'http://www.twoscoopscreamery.com', '1592846734', '1592846740', None, 'http://www.dazzlingnailsandspa.com', None, None, 'http://www.thepressboxnc.com', '1592846762', 'http://tasteseduction.wixsite.com/tasteseduction', None, 'https://www.codeninjas.com/locations/pa-wexford', None, 'https://www.simonmed.com/locations/all/simonmed_imaging__centennial', 'http://www.dollar.bank', 'http://www.gamestop.com', None, 'http://www.brassarmadillo.com/shop/phoenix-az', None, 'http://www.tapatiocliffshilton.com/dining/pointe-in-tyme', None, 'http://www.hottiesworld.com', 'http://www.rivierahotel.com', 'http://www.kungfunoodles.ca', 'http://blindpigbrewery.com/brewery.html', 'http://www.hubbardexteriors.com', 'http://www.habaneros.mx', 'https://locations.panerabread.com/oh/medina/4065-pearl-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'https://www.compassselfstorage.com/self-storage/pa/pittsburgh/fifth-ave/', 'http://www.starbucks.com/store/9298/', '1592846846', None, 'https://www.celestialsolar.com', 'http://fortmillprep.com', 'http://www.portofsubs.com', 'http://www.hollywoodsmiledentallv.com', 'http://www.sammyspizza.com/location/las-vegas-flamingo', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', '1592846873', 'http://www.escapeadventures.com', None, 'http://deansilvermd.com', 'http://www.boriskosher.com', 'http://www.senatorsinn.com/', '1592846894', 'https://www.macaronigrill.com/locations/location?id=232', 'https://locations.mrtire.com/oh/solon/6120-som-center-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'http://www.duggansbrewery.com', 'http://www.inoroutpetproducts.com', 'http://www.hmflooringgroup.com', 'http://www.usps.com', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB08', 'http://www.palaceonpape.ca', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://88imarket.com', 'http://prioritymovingstorage.com', None, '1592846943', None, 'http://calstate.aaa.com', 'http://www.barreworks.ca', 'http://www.urbanassaultpb.com', 'https://photographybyjodilynn.com', 'https://www.mark-taylor.com/apartments/az/phoenix/san-paseo/', 'http://www.bedbathandbeyond.com', 'http://divanailsglendale.com', None, None, None, 'http://union.illinois.edu/techzone/', 'http://www.mountainviewfuneralhomeandcemetery.com', 'http://www.culvers.com/restaurants/champaign-marketview', None, 'https://www.culinarydropout.com', 'http://www.ocotillodancecenter.com', None, None, None, 'http://www.averylanehome.com', None, None, 'http://www.TheRainmakerInstitute.com', 'https://rewindtreats.com', None, None, 'http://www.maac.com/north-carolina/charlotte/colonial-village-at-matthews?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://www.greulichs.com/', None, 'http://thelocalbarberandshop.com', 'http://www.discoverykidslv.org/', 'http://www.bowvalleyaquarium.ca', 'http://www.5thelementt.com', 'http://www.cellcomrepair.com', 'http://tnasmokeshop.wix.com/traderssmokeshop', 'http://www.edge102.com', None, 'http://www.friendlypawspetresort.com', 'http://www.billjohnsons.com', 'http://www.labrestaurant.com/', None, None, None, 'http://www.dickssportinggoods.com/', 'http://Www.SerenityRichmond.com', 'http://www.jiffylube.com', 'http://www.ridenowsurprise.com/', None, None, 'http://www.gullivergaragedoorscalgary.com', 'http://www.cookiescoop.ca/', 'http://www.worldtravelmates.com', '1592847116', 'http://www.twobitesaloon.com/', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://camelbackanimalcenterphoenix.com', None, 'http://www.bedbathandbeyond.com', None, 'https://centerfoldscabaretlv.com', 'http://www.yogainnovations.com', 'https://www.kebaberie.com', 'http://www.ypcatering.com', 'http://www.sportswap.com', 'http://www.applebees.com/', 'http://www.stamoolis.com', '1592847166', 'https://www.lafitness.com/Pages/findclubresultszip.aspx?state=ON', 'http://www.oliviers.ca', 'https://charliemaesoulfood.com', None, 'https://www.gowireless.com/stores/nv/north-las-vegas/north-las-vegas-aliante-marketplace/', 'http://www.elyriaford.com', 'http://www.jollygoodscandy.com', None, 'http://www.velkconstruction.com', None, None, 'http://www.nicediggz.com', None, None, 'http://www.bumpkins.ca/', None, 'http://www.theacademydayschool.com', 'http://www.phxlib.org/Locations/Pages/Juniper.aspx', None, 'https://www.wellsfargo.com', 'https://www.diamondresortsandhotels.com/Resorts/Scottsdale-Villa-Mirage?MKC=YELPUS', None, 'http://www.monroestreetframing.com', 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=300', None, None, None, 'http://www.parentscanada.com/sweetdeals', 'http://www.offchutetoo.com', 'https://www.motel6.com/en/motels.az.scottsdale.29.html', 'https://www.getbellhops.com/market/phoenix-arizona?utm_source=yelp&utm_medium=paid_referral&utm_enhancedprofiles&utm_content=businessurl', 'http://iloveyogurtys.com/', 'http://brotherstwosmallengines.ca', 'http://www.JeffMykell.com', 'http://oscarcatering.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.azhealingcenter.com', 'https://www.dekalash.com/find-a-studio/arizona/promenade', 'http://richtreenaturalmarket.com', 'http://www.calvinkleinretailstores.com', None, None, None, 'http://www.saguarocarwash.com/', 'https://iris.ca/en/find-a-store/north-york-st-gabriel-terraces', None, None, 'https://www.simonmed.com/locations/all/simonmed_imaging___paradise_valley', None, 'https://cobblestone.com/?utm_source=yelp%C3%8A', None, 'http://www.quiktrip.com', 'http://maizemexicangrill.com', None, None, 'https://www.bootbarn.com', 'http://www.satyrentertainment.com', 'http://www.FiestaLincoln.com', 'http://www.shopko.com/custserv/store_details.jsp?storeId=74', 'https://www.backroadcoffee.ca', 'http://www.prioritypumpingaz.com', 'https://locations.vitaminshoppe.com/nv/lasvegas/vitamins-supplements-las-vegas-nv-394.html', 'http://www.landy.ca', 'http://www.dimefurniture.com', 'http://www.777cars.net', None, '1592847386', 'http://luxuryspraytan.com', None, 'http://www.arbys.com/', 'http://www.doctorautolv.com', '1592847399', 'http://walmart.com/', 'http://www.jwlasvegasresort.com', 'http://pinkhousecrewsnc.com', 'http://www.upperdeckon6th.com', 'http://www.washngo43.com', 'https://www.maccosmetics.com', 'https://www.hotglassalley.com', None, None, 'https://www.12thmanhooligans.com', None, 'http://www.beautykouture.com', 'http://www.launicaballantyne.com', 'http://www.ntb.com/store/8535/mentor-oh-44060-7523?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, 'http://www.centrerockland.com', 'http://www.crabbyjoes.com', 'http://www.saffronindianfood.com/', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', 'http://www.mcdonalds.com', None, '1592847466', 'https://bostonpizza.com/en/locations/sunridge.html', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', None, 'http://www.rotblotts.com', 'https://dukesrefresher.ca/st-lawrence-market/', None, 'http://www.lionandblue.com', 'http://www.clarklawaz.com', None, None, 'https://bangkokburi.com', '1592847501', '1592847504', None, None, 'https://www.floodsurbanseafood.com', 'https://www.saludmexicanbistro.com', None, 'http://www.maddenendurance.com', None, None, 'http://www.hand2sole.com', 'http://www.thecyclepath.net', 'http://www.excellohio.com', 'https://www.canwise.com', None, 'http://www.valvistadental.com', 'http://www.nsendodontics.com', None, 'http://theyardstylist.com', 'http://www.theboilbar.com', 'http://www.pizzabrutta.com/', 'http://www.easybreakfastrestaurant.com', '1592847571', 'https://www.ig-law.com', '1592847579', '1592847582', 'http://raysautoandtruck.com', 'http://www.takashi.ca', 'https://www.solisatflamingo.com', None, 'http://inoroutmoversphoenixmetro.com', 'https://www.popeyes.com', None, None, 'http://www.tedsexcellentbikerepair.com', 'http://www.palmsatpeccoleranch.com/', 'http://www.kollectivestudio.com', 'http://www.asapenterpriseshomeimprovements.com', 'http://www.marriott.com/hotels/travel/cltfm-fairfield-inn-and-suites-charlotte-matthews/', None, 'http://diamondbackflooring.com', 'http://www.TheReserveatProvidence.com', None, None, None, None, 'http://www.misosushiandgrill.com', 'http://arizonaanimalhospital.com', None, 'http://www.secretgardenevents.com/', 'https://www.appliancerepairservicehudson.com', None, None, 'http://sportsandfitnessclubs.com/locations/university.php', 'http://www.kfc.ca/store/1330-mcphillips-st-winnipeg', 'https://roadhousecinemas.com', 'http://www.pawsattraction.net', 'http://www.whitewheel.com/', 'https://www.pizzahut.ca/store-details/store-R31403/pizza-hut-Thornhill', None, 'http://www.k9hair.com', None, 'https://bostonmarket.com/location/glendale-az-2407/', None, 'http://www.kasbys.com', 'http://eatdrinkmargaritas.com', 'https://www.starbucks.ca', None, 'http://www.passportcafepittsburgh.com', None, 'https://www.modernwellnessclinic.com', 'http://www.nickirmt.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://ajlawplc.com', 'http://thelube.com/locations/ohio/medina-township/', 'http://www.lechaperonrouge.com', None, 'https://wineanddesign.com/locations/gastonia', 'http://www.gamestop.com', 'http://www.haroldsflorist.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, None, None, None, 'http://www.wheelhouse702.com', None, 'http://www.fresh.com', 'http://www.discounttire.com', 'http://www.performancerealtynv.com/', 'https://sealoutscorpions.com', None, 'https://www.striphouse.com/venues/las-vegas', 'http://www.clevelandautoshow.com', None, '1592847807', 'http://www.divasanddudeskidshairsalon.ca/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.drivepetty.com/race-tracks/las-vegas-motor-speedway?utm_source=yelp&utm_medium=cpc&utm_campaign=lasvegas', '1592847820', 'https://www.corepoweryoga.com/free-week?utm_source=yelp&utm_medium=cta&utm_campaign=old-town-scottsdale-yelp-free-week', 'http://www.extramilepaintingcompany.com/', 'http://www.kiaofgastonia.com', 'http://www.ilovelavish.com', None, 'http://www.azallergy.com', 'http://www.vibo.ca', 'http://www.bigtwotoyota.com/', 'http://www.soldbyowens.com', 'http://phoenix.clscars.com/standard/home.aspx', 'http://www.starbucks.com/store/11135/', None, None, 'http://www.yorkgatemall.com', 'http://www.creativeillusionsllc.com', 'https://800degrees.com/locations/', 'http://www.banthateabar.com/', None, 'http://www.arlintcpa.com', 'http://bit.ly/3aqlmiO', 'http://www.stephaniedaninehair.com/', 'http://www.tumi.com/', None, None, 'http://www.hotcards.com', 'http://silverstateneurology.com', 'http://www.PhotographyByJake.com', 'https://locations.wendys.com/united-states/sc/clover/5188-charlotte-highway', None, 'https://tedsrefreshments.com', None, 'http://www.pawsandclawswi.com/', 'http://www.nadege-patisserie.com', None, 'https://www.bannerhealth.com/locations/chandler/banner-urgent-care-7', 'http://www.starbucks.com/store/11135/', 'http://bobaboy.ca', None, 'http://www.latitude36lkn.com/', None, 'https://www.bannerhealth.com/locations/gilbert/banner-urgent-care-2', 'http://urbanfringesalon.ca', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.asianbbqbuffet.com', 'http://www.costcutters.com/', 'http://www.ampm.com', 'http://onestopnutrition.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89118/838028/', 'http://www.alphabetcity.org', None, 'http://www.lvpaiutesmokeshop.com', None, None, None, None, 'http://www.valleyheart.us', None, 'http://www.speedway.com', 'http://www.dvrphx.com', 'http://schwatailorshop.com', None, '1592848042', None, None, 'http://www.boxcarsocial.ca/', 'https://www.walmart.com/store/5747/locust-nc/details', None, None, 'https://www.yorkvilleoralsurgery.com', None, 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', 'http://www.strangerootsbeer.com/taprooms/millvale/', 'http://www.hawthornespizza.com', None, 'http://www.AR500Armor.com', 'http://locations.atipt.com/washington-vegas-nv', None, 'http://www.goodwillgoodskills.org/contact-us/find-a-location/painesville-township.aspx', 'http://www.astoriashishkebobhouse.com/', 'http://www.gnc.com', '1592848106', None, 'http://www.craftyburgr.com', 'http://www.thepetshopaz.com', 'https://local.fedex.com/il/peoria/office-0224/?cmp=LOC-1001545-3-1-971-1110000-US-US-EN-YEXTLISTFXOPRSC', 'http://hyaface.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.shalimarcountryclub.com', None, 'http://www.annieaime.com', 'http://forgesocialhouse.com', 'https://my.clevelandclinic.org/departments/cancer/patient-education/palliative-supportive-oncology/hospice-of-cleveland-clinic', None, None, 'http://www.gatescollision.com/auto-body-locations/sun-prairie-wi', 'http://www.oliveriobuick.com/?cs:pro=repman&cs:e=yelp', None, 'https://www.walmart.com/store/1385/gastonia-nc/whats-new', '1592848169', 'https://www.yournevadacpa.com', 'http://www.team-k9.com', None, 'http://www.customcakesonline.com', 'https://locations.mrtire.com/oh/mentor-on-the-lake/5969-andrews-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'http://www.husnus.com', None, None, 'http://www.georgiosofp.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://thewgallerycle.com', 'http://www.chadastreet.com/', 'http://www.kayamono.ca', 'http://www.goddessblessedinc.com', 'http://www.terrajava.biz', 'http://www.coxendo.com', 'http://www.cszlasvegas.com', 'http://www.arkadiahouse.com', 'http://www.lasvegaspolestudio.com', 'http://www.liveatescape.com', 'http://www.madephx.com', 'http://www.cottonandcopperaz.com', None, 'http://uniqtailors.ca', 'https://nationwidevision.com/locations', 'https://www.autozone.com/locations/oh/cleveland/16122-lakeshore-blvd.html', 'http://therapytreeaz.com', 'https://www.azbounce4kids.com', 'http://1416centre.ca/stores/the-mens-hairstylists', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', None, None, 'http://conradsgrill.com', None, '1592848286', 'https://www.kohls.com/stores/nv/northlasvegas-1130.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.theparkvegas.com/en/restaurants/beerhaus.html', None, None, 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'http://www.fido.ca', 'http://www.banfield.com/veterinarians/az/gilbert/gil?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://local.safeway.com/safeway/az/scottsdale/23565-n-scottsdale-rd.html', 'http://www.kfc.ca/store/422-bayly-st-ajax', 'http://www.guardomatic.com', 'http://jobhuntrphx.com/home', 'http://www.restomonami.com', None, 'http://www.paymons.com', 'http://www.thebarat2132.com', None, 'http://www.takarabune.ca/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.aocphysicians.com', None, 'http://www.phoenixmenshealthcenter.com', None, None, 'http://www.thompsonlandry.com', None, 'http://www.marshallsonline.com', 'https://bcss702.com', None, None, None, 'http://www.bowlology.com', 'http://www.berchicci.ca', 'http://www.smilesdentalgrouplasvegas.com', 'https://chrisluk.com', 'http://www.ramada.com/hotels/hotel-overview?hotel_id=45300&cid=whg_ram_yelp-cta&wid=ps:addppc_yelp-cta&tel=8002521709&reg=appc-_-YLPROPP-_-45300-_-RAMENCT', 'http://www.sushiaveaz.com', 'http://www.chandlersmallanimalclinic.com', 'https://redrock.sclv.com/Dining/Feast-Buffet?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', None, None, 'http://www.slimans.net', 'https://www.lexusoflasvegas.com', None, None, 'http://tonysaccos.com/pizza-locations/concord-nc/', None, 'http://www.rougevalley.ca', 'http://www.thebarlv.com', 'http://www.electrolysisdermacare.com', 'https://sincitysmash.com', 'http://www.jewelryhospital.webstarts.com', 'http://www.quiktrip.com', None, None, None, None, 'http://www.epiphaniechocolate.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.salvedgefashion.com', None, 'http://www.calgarylabservices.com/', 'http://www.rockyriverwellness.com/', None, 'http://www.bk.com', 'https://teamprostruct.com', 'https://www.chick-fil-a.com/wesleychapelweddington', 'http://www.az-solarcontrol.com', '1592848516', 'http://www.ntb.com/store/8531/cuyahoga-falls-oh-44221-4916?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', 'http://www.elitelashstudioaz.com', 'http://loscafetaleros.com', None, 'https://bbschl.com', 'http://redringrestaurant.com/', 'http://www.labcorp.com', None, None, 'http://leenailscharlotte.com', None, 'http://www.nirvanaairbrushtanning.com/', None, 'http://www.marcs.com/stores/marcs-elyria-grocery-store-44035.aspx', 'http://www.luxridesaz.com', 'http://angelosgilbertbarbershop.com', 'http://tasteaboba.com', 'http://www.elchavotortas.com', 'https://rallys.com/locations/nv/las-vegas/4175-e-desert-inn-rd/', 'https://emeraldharvest.com', 'https://local.albertsons.com/az/chandler/3145-s-alma-school-rd.html', None, 'http://www.pugzies.com', 'https://www.urbanbarn.com/en/stores-detail/?id=C503', 'http://www.potbelly.com/Camelback?utm_source=ExtNet&utm_medium=organic&utm_campaign=Yext', 'http://www.laesquina.ca/', 'https://www.praguerestaurant.ca', 'http://www.premiereautoglass.com/', '1592856451', 'https://www.slateclt.com', 'https://el-charro-mexican-grill-restaurant.negocio.site', 'http://PuharicPlumbing.com', '1592856464', 'http://www.RedRockManagementLV.com', 'http://www.thestuffedolive.ca/', 'http://www.ixcenter.com/', 'http://www.wazeesworld.com', 'http://www.sunsationalswimschool.com/los-angeles-swimming-lessons.php', None, 'http://www.allseasonautos.com', 'http://www.mcvayplumbing.com/', None, 'http://Greenvalleyfertility.com', None, 'http://www.addisonpestcontrol.com/', 'http://walltowallvegas.com', None, 'https://gordonbiersch.com/locations/gilbert/', 'https://parkmgm.mgmresorts.com/en.html', 'https://mckeedental.com', 'http://www.unitedtalentcanada.com/', None, 'http://www.threes-company.com', 'http://crossfit704.com', '1592856522', 'http://www.costaverde.ca', 'https://stores.savers.com/on/oakville/valuevillage-thrift-store-2095.html', None, '1592856532', None, 'http://rivaldatiles.com', None, 'http://www.immaculatedetailingpgh.com', 'http://www.toronto.ca/parks/prd/facilities/complex/306/index.htm', 'http://www.middypools.com', 'http://www.gutterforce.com', 'http://locations.michaels.com/wi/middleton/3745/', 'http://www.artofacupuncturecharlotte.com', None, 'http://aapglv.com', 'http://www.creditlandinganimalhospital.com', 'http://www.lapetite.com/your-local-school/chandler-az-7659/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, 'http://www.simplycleanorganic.com', 'http://www.ganleybedfordimports.com/', 'http://smautobodync.com/', None, None, 'https://santafestation.sclv.com/?utm_source=YELP&utm_medium=SOCIAL&utm_term=SF&utm_content=SF-PROPERTIES&utm_campaign=SF-YELP', 'http://foodbenders.com/', None, 'http://quinnbrewing.com', '1592856593', None, 'https://oralsurgerymadison.com', 'https://www.papajohns.com/international', None, 'http://www.mrhero.com', None, 'http://patetekitchens.com', None, None, None, 'http://www.buzzberry.com', 'http://www.mattressfirm.com', 'http://Www.mobileifixers.com', 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://jeffohmhomeloans.com', None, None, None, None, None, 'http://www.modernfamilydentalcare.com', 'https://www.thejoint.com/arizona/chandler/ocotillo-48017', 'https://www.rentawreck.com/cheap-car-rental-parma-OH.htm', 'http://www.nyxecigs.com/vape-store-yonge-finch-north-york-nyx-ecigs-e-cigarettes-e-liquid', 'https://www.desertmirageapartments.com', 'https://www.billluketempe.com', 'http://rocketfizz.com/locations/rocket-fizz-homestead-pa', 'http://www.bangkokgarden.ca', 'http://www.hairbooth.ca', 'http://iptaz.us/', '1592856665', '1592856668', 'http://www.wegotmail-llc.com', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85331/790-in-cave-creek/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-790&utm_content=website-link&howheard=IYE', 'http://www.ilboscoristorante.com', None, 'http://www.timhortons.com', None, 'http://grangenailbar.com/', 'http://amazingclowns.com/', 'http://www.dooney.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://pittsburgh.improv.com?ref=3A0E697E28853742E787C828543590BCB4A793C5B1617D1E1E6CC79218A846B2', 'http://www.carospartycenter.net', None, None, 'http://www.detailgaragemesaaz.com', 'http://www.deltaco.com', 'http://www.lasvegashomesearchandservice.com', 'http://www.michaelscreative.com', 'http://tempeautorepair.biz', 'https://demetres.com/locations/mississauga-centrum', 'http://www.hyeholde.com', 'http://www.sonoranoutdooradventures.com', 'http://greatharvestlvnorth.com', None, 'http://www.kensautoserviceohio.com', 'http://www.restorationhardware.com', '1592856733', None, 'http://southendwinefest.org', None, 'http://edentherapyandmassage.com/', 'http://www.midas.com/toronto/store.aspx?shopnum=9194&dmanum=857001', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=cltdt&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'http://www.balancebytouch.com', 'http://www.strosepeds.com/', 'http://www.tuliphomecleaning.squarespace.com', None, 'https://www.smartstyle.com/en-us/locations/nv/las-vegas/located-inside-walmart-3473-haircuts-3334.html', 'http://www.calgarytransit.com/', None, 'https://locations.theupsstore.com/nc/mint-hill/7427-matthews-mint-hill-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://downtownchandler.org/farmersmarket/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'https://us.petvalu.com/location/6033', None, 'http://www.petco.com', None, 'http://www.pediatrixmd.com', None, 'http://petuno.com', 'http://thebakehousetoronto.com', None, None, 'http://www.mountainsidewellnessaz.com', 'http://www.spectrum.com/?cmp=yxt', 'http://www.summitrestorationaz.com', None, 'http://breakfastjoynt.com/', None, None, 'http://regalnailslasvegas.com/', 'http://www.onenevada.org', None, None, 'http://www.scrunchdawgs.com', 'http://eggstasyaz.com', None, 'http://rockndeli.com/', 'https://www.sassycowcreamery.com', 'http://imperialengravers.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.azprideinsulation.com', 'http://www.hyartgallery.com', 'http://www.3rdplacegrill.com', None, 'http://garbagetruckfoodtruck.com/charlotte-coming-soon/', 'http://www.tatumdrugs.com', '1592856865', 'http://www.costco.ca/WarehouseLocatorDetailsView?langId=-24&storeId=10302&catalogId=11201&warehouseNumber=526&BeginAddress=L5R%203S9&numOfWarehousesToReturn=5&location=L5R%203S9&callingPage=WarehouseLocatorView', 'http://www.pokepoku.com', 'http://www.signaturenorthwest.com', 'http://www.sibleyswest.com/', 'http://www.pupcuts.com', 'http://BladeMasterslv.com', None, 'http://www.partycakeshop.com/', 'https://www.catalystcharlotte.com', '1592856890', 'https://agents.allstate.com/yuqing-zhang-las-vegas-nv.html', 'http://www.questdiagnostics.com', None, 'https://www.hilton.com/en/hotels/phxgzht-home2-suites-gilbert/?SEO_id=YELP-HT-PHXGZHT', 'https://www.orangetheory.com/en-us/locations/north-carolina/cornelius/20619-torrence-chapel-rd/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.christinecowernteam.com', 'https://www.caesars.com/paris-las-vegas?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=ParisLasVegas&utm_content=hotel', None, None, 'https://liquidateaz.com', 'http://www.azspineandjoint.com', 'http://local.g4s.us/Charlotte', None, 'http://www.oliveoil.com', None, 'https://www.target.com/sl/parma/792', '1592856931', 'http://peoplespint.com', None, None, None, 'http://www.srhodesdds.com/', None, None, 'http://www.cprnlv.com', 'http://www.goodwillaz.org', None, 'http://fountinis.com', 'http://www.broachsportstours.com', 'http://www.umisushiexpress.com', 'https://jenny-q-beauty.business.site', 'http://www.smoothieking.com', None, 'http://www.jenkinslawnandgarden.com', '1592856985', None, None, 'http://www.mipworldwide.com', 'http://qualitymaids.net', 'https://www.carkeyreplacementllc.com', 'http://www.plantmanco.com', 'http://www.balsonbeer.com', None, 'http://www.avantipizzalv.com/', 'http://www.tuttifruttidejeuners.com/en/', None, None, None, 'http://www.heroescalgary.com', None, 'http://www.lullabylane.org', 'https://jjnailsparobinson.business.site', 'http://lvbraces.com', None, 'http://www.leasureportraits.com', 'http://www.drgoldman.com/', 'https://www.ienate.com', None, 'http://www.greenvalleydentistry.com/', 'http://www.piwhaz.com/', 'http://www.lgpreschools.com/', None, 'http://www.licedoctors.com/arizona/phoenix-lice-treatment-service.html', 'http://www.brewnutscleveland.com', 'http://www.garnerorthodontics.com/chandler-orthodontist', None, 'http://toursofdistinctionlv.com', 'http://bianuccisalon.com', 'http://starlimorepair.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://www.homedepot.com/l/Cave-Creek/AZ/Phoenix/85022/480?cm_mmc=seo-yelp&', None, None, None, 'http://onestopnutrition.com', None, None, None, 'https://www.antiquetrove.com/scottsdale', None, 'http://www.snapcareclinic.com/', None, 'http://massagemaniaglendale.com', 'http://Lanawongdds.com', 'http://www.uwhealth.org/eyecare/uw-health-optical-shops/12457', 'http://www.thompsongroupaz.com', 'http://www.premiumsweets.ca', 'https://wildelkden.com', '1592857120', 'https://www.psdm-dolce.com', 'http://www.familydollar.com', None, None, 'http://www.paradisefamilydental.com', 'https://www.lawndoctor.com/madison-wi', 'http://lekebabgrill.com/', None, 'http://www.sotoviolins.com', 'http://www.bk.com', 'http://www.butteravenue.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=2821&utm_content=bpas', 'http://www.piscespets.com', 'http://www.sugardaddysfoodtruck.com', 'http://www.rei.com/henderson/', 'http://arizonarug.com', 'http://www.drlaffa.com', 'http://www.davemacspowerwashing.com', None, 'http://www.ridenow.com', 'http://www.EarnhardtFord.com', 'https://www.vollersmiles.com', None, None, '1592857184', 'http://www.cleantilearizona.com/', 'http://www.parksidesouthtryon.com', 'http://www.xtremegymnastics.com', None, 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_638', None, None, 'http://www.premahealth.ca', None, 'http://www.detoxforlife.biz', None, None, 'http://www.mckensmexicangrill.net', 'https://www.panerabread.com/en-us/home.html', 'http://www.nourishcreameryandjuicebar.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/16545+East+Palisades+Boulevard-Fountain+Hills-AZ-85268/storeid=9279?cid=ps_ylp_2020', 'http://scalpmicropigmentationcenter.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.theartofshaving.com', None, 'http://www.globalpetfoods.com', 'http://www.laparmigiana.yolasite.com', None, None, 'http://www.otaninoodle.com', 'https://www.peckfamilydentistry.com', 'https://locations.rallys.com/az/mesa/343-west-mckellips-road', 'http://www.chardonlakes.com', 'http://www.advantagebeautyandhealth.com/', 'http://www.superstore.ca', '1592857259', 'http://vernlewis.com', 'http://www.holysheetsusa.com', 'http://www.secondcity.com', 'http://www.indigokeys.com', 'https://www.yelp.com/events/matthews-charlotte-food-fight', 'http://www.rossstores.com', '1592857279', '1592857283', 'http://www.gong-cha.ca', 'http://www.vegasdiscountnutrition.net', 'http://www.inkaheritagerestaurant.com', None, 'https://www.escapology.com/en/mentor-oh/', None, 'http://www.btblv.com', 'https://www.bannerhealth.com/locations/surprise/banner-urgent-care-1', 'https://www.chocolatsfavoris.com/fr', 'https://www.kumon.com/LAS-VEGAS-RHODES-RANCH', 'http://www.oreillyauto.com', 'http://www.supermat22.com', None, 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreID=930', 'http://www.happykidentertainment.com', 'https://www.theneckandbackclinics.com/locations/aliante', None, 'http://www.miracleinprogress.com', 'http://www.pinecleanersdelivery.com', 'http://www.banfield.com/veterinarians/az/chandler/cnd?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://breakoutgames.com/charlotte', 'http://blacktoerunning.com/', 'http://www.freddysusa.com', 'http://www.waffleshop.org', None, 'http://outlawclassiccars.com', 'https://www.metro.ca/en/find-a-grocery/342', 'http://www.blueburrito.com', '1592857368', 'http://www.longos.com', 'http://phoenixgreekfestival.org', 'https://nationwidevision.com/locations', 'http://www.pandora.net/en-ca/stores/pandora-square-one', 'http://www.midas.com/lasvegas/store.aspx?shopnum=1192&dmanum=480', None, 'http://www.lornescoats.com', None, 'http://www.cremacalgary.com', '1592857402', 'http://www.wrightgmcbuick.com/', None, 'http://puttersmedina.com/', None, None, 'http://www.thesalooncharlotte.com/about.php', 'http://www.jambajuice.com', '1592857430', None, 'http://www.sunstatepools.weebly.com', 'http://www.expressbailagency.com', 'http://www.bodyvision.ca/', 'http://www.lacoiffe.com', '1592857452', 'http://www.starbucks.com/store/9298/', None, 'http://www.puffs-n-stuff.com', 'http://bellagio.com/restaurants/circo.aspx', 'http://www.kwiktrip.com/Locations/?searchtext=53598', 'http://www.timhortons.com/', 'http://www.atlantictrapandgill.com', 'http://www.suncoastdentalaz.com', 'http://www.beanzcc.com', 'http://www.winghouseandsportsbar.com/', 'http://thelodgesasquatchkitchen.food-places.com', '1592857502', '1592857506', None, 'http://www.highparkclub.com', 'http://entscottsdale.com', 'https://www.dollartreecanada.com/', 'http://www.palermos67.com', None, 'http://www.dylamatosmarket.com', 'http://www.solsticetavern.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.shopthesecretvillage.com', 'https://www.canadianappliance.ca/Showroom/Canadian-Appliance-Source-Etobicoke', None, 'http://www.heartlandcu.org', 'https://www.angrypipe.com', 'http://www.goodwillgoodskills.org/contact-us/find-a-location/strongsville.aspx', None, 'http://www.coffeebean.com', 'http://www.aspenluxesalon.com', None, 'http://www.justmarried.vegas', 'http://www.sarkujapan.com', 'http://www.cookiezoo.com', 'http://www.royalcoffeebar.com/', None, 'http://www.theresasbakery.com/default.html', None, '1592857606', None, None, 'http://catermeicecream.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.fountainhillsrecovery.com', 'http://www.tropiczoneparrots.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.culvers.com/restaurants/madison-east-towne', 'http://www.smartreit.com/shop/property/mississauga-meadowvale', 'http://drfleas.com', None, 'http://www.201central.com', None, 'http://www.fairsfair.com', 'http://www.rexall.ca/storelocator/store/1313', None, None, 'http://www.timelesslaserskin.com/', 'http://www.shirtail.com', None, 'https://ayiddishemame.com', None, 'http://bluegoosepurefoods.com', 'http://www.toronto.ca/parks/prd/facilities/complex/196/index.htm', 'http://www.commercialhardwaregroup.com', 'http://www.timhortons.com/', None, None, 'https://palo-verde-lounge.business.site', None, None, None, 'http://www.midwoodautocraft.com', 'https://exclusivebarbershopandgrooming.ca', 'http://thebrubakerspub.com', 'https://www.clubpilates.com/hampton', 'http://www.lambertgm.net', 'http://frijoles.vegas', 'http://lolaseatery.com', 'https://www.riseonapache.com/?utm_knock=y', 'http://www.drshariwebster.com', None, 'http://www.bolleswimschoolinternational.com', 'http://www.prolicemom.com/', 'http://www.mrsmalls.com', 'http://www.loschiludos.com', 'https://calstate.aaa.com/?=yelp_track', None, None, 'http://kidtokid.com/summerlin/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.villagerestaurantclt.com', 'http://www.lifecareforwomen.com', 'https://www.rubytuesday.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.handelsicecream.com/', 'https://charleyssportsgrill.com', 'http://www.previewarizonahomes.com', 'http://www.hautecoffee.ca', 'http://madpowertraining.com', 'http://www.canadatailoring.ca', 'http://leenasfood.food94.com', 'http://thespystore.ca', 'http://www.sugarfactory.com/', 'http://www.skepticalchymist.com', 'http://www.functionaltrainingstudio.com', 'http://www.vault9cle.com/', None, 'https://www.armandoscle.com', None, None, 'http://www.chandleraz.gov/default.aspx?pageid=292', 'http://donramon-granfiestamex.com', 'http://gilbertpizzaaz.com', 'http://eggstasyaz.com', 'http://www.caesarspalace.com', 'http://963kklz.com', 'http://www.patisseriedolcesapore.com', 'http://www.FlirtHairSalon.com', 'http://www.villageemporiumcharlotte.com', 'http://mylincolnbakery.com/', 'http://www.theivyatverity.ca', None, 'http://www.queensheadpub.ca/', None, 'http://nesilv.com', 'http://spinalrepairshop.com', 'http://www.sandquistdds.com', 'https://calstate.aaa.com/?=yelp_track', None, 'http://www.maxandermas.com/locations/333038', None, 'http://gregjockel.com', None, None, None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1015+East+Ray+Road-Chandler-AZ-85225/storeid=7849?cid=ps_ylp_2020', None, 'http://www.chandleraz.gov/aquatics', None, 'http://www.corminair.com', None, None, 'https://slotburger.com', 'http://Www.blossom-moments.com', None, 'http://fourseasonsac.ca', 'http://www.cobsbread.com/local-bakery/kingsland-calgary', 'http://www.gunmountain.com', 'http://www.mrhandyman.com/local-handyman-service/pa/northern-pittsburgh.aspx', 'http://www.averagebroz.com/', 'http://www.issmi-sushi.com', 'http://www.josephineskaught.com', 'http://www.starbucks.com/store/8054/', 'http://www.xtrememovers.xyz', 'http://www.petalsyorkville.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://nevadaretinacenter.com', 'http://www.rizepizza.com/', 'https://www.enterprise.ca/en/car-rental/locations/canada/qc/north-montreal-saint-michel-c720.html?mcid=iyp:8368400', 'https://www.winners.ca', 'http://www.cosmoscafe.com', 'http://www.booth121.com', 'http://www.networkautomotive.com', 'http://www.racedaydetailing.com', 'http://www.nhcclv.com', 'http://www.usquaremadison.com', 'https://railroadpass.com', 'https://www.davidyurman.com/stores/s/david-yurman-the-forum-shops-at-caesars?ecid=listing%20marketing%20store%20LasVegas%20all%20082216%20all', 'http://www.coleonespizza.com', 'http://www.rinaldisdeli.com/', 'http://www.bigjimscustomexhaust.com', 'http://www.azbigfish.com', None, None, 'http://www.striptrips.com', '1592858092', 'http://www.palatecleveland.com', 'http://www.isabellatoronto.com', 'http://www.bestairlineshuttle.com', 'http://www.empirechef.com', 'http://www.amcdowelldental.com', 'http://www.nassarmd.com', None, 'http://www.snapfitness.com/lasvegas6', 'http://www.jasonpaszek.com', None, None, 'http://www.discountaquariumsaz.com', 'http://www.eybmassagetherapy.com', 'http://www.terribleherbst.com/', 'https://johnnysmithdental.com', 'https://www.thebodyshop.com/en-us/?utm_source=yelp&utm_medium=yelp&utm_campaign=us_180418_w19_search_bau&utm_content=websiteurl', 'http://robertostacoshop.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281380115&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.epropertiesdev.com/', 'https://www.drstephenmiller.com', 'http://www.kmspatherapy.com', None, None, 'http://desertvalleyaire.com', None, None, 'http://www.houstonelectriclv.com', None, 'http://www.palomamexicanrestaurant.ca', 'http://www.extremerestaurantandcatering.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592858218', 'http://www.toysrus.com/family/index.jsp?categoryId=2255956&camp=MISC:yelp:store:page:tru:111910', 'https://www.henrys.com/stores/1-Toronto.aspx', 'http://www.ss106.ca', 'http://parisnailslasvegas.com', None, 'https://www.sportchek.ca/stores/leaside.html', 'http://serenity-hairdesign.com/', None, None, 'http://www.castletoys.ca', 'http://www.idealcoffee.ca', None, 'http://www.thebigbangbar.com/az/tempe', None, 'https://blinkmattressexpert.com', 'http://www.bombaybhelrestaurant.com', 'http://pastapronta.ca', None, 'http://www.maids.com/274/', 'http://www.k9katelynn.com', 'https://www.circuscircus.com/en/restaurants.html', 'http://www.costco.ca/WarehouseLocatorDetailsView?callingPage=WarehouseLocatorView&storeId=10302&BeginAddress=T1Y+6Z7&langId=-24&location=T1Y+6Z7&warehouseNumber=56&catalogId=11201&numOfWarehousesToReturn=5', 'http://www.bk.com', 'http://www.usps.com', 'http://www.superior-tire.com', None, 'http://www.arizonadigestivehealth.com/about-us/corporate-office', 'http://www.rootshair.ca', 'http://www.randysroti.com', 'http://storelocator.staples.ca/stores/en_CA/AB/Calgary/132', 'http://www.fivebelow.com/', 'http://sunsetpizzeriaonline.com/', None, 'http://www.primequarter.com', None, 'http://jackandjillshauntedhill.com/', 'http://www.city-tavern.com', '1592858350', None, 'http://www.gentleazdentist.com', 'http://www.lusciouslockshair.com', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', None, 'http://www.brunospizzagibsonia.com/', '1592858374', None, 'https://hotelxtoronto.com/en/dining.html', 'http://customautomatedsolutions.net', 'http://www.oreillyauto.com/', 'http://glendaleazpaintingcontractor.com', 'http://www.smokeawayaz.com', '1592858399', 'http://www.wineandcanvas.com/charlotte-nc.html', 'https://www.bobevans.com/our-restaurants/locations/585?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.azcentralcu.org/home/arizona-locations/bell-road-glendale-az-branch', 'https://www.americasbest.com/store-list/charlotte-north-nc-28216', 'http://www.revelationcommunitymanagement.com/', '1592858424', None, None, 'http://handyazman.com', None, 'http://www.familyautocareaz.com', 'http://www.smithbrotherssteakhouse.com/', 'https://stores.theory.com/1159408-theory-las-vegas', 'http://www.chicksauto.com/', 'http://www.coolcuts4kids.com/salondetail/default.asp?salonid=66008', 'http://www.newyorkfries.com/locations/view/25', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'http://triplejcarpetcleaning.com', '1592858482', 'http://www.coffeepriestcharlotte.com', None, 'http://superone.ca', 'http://www.thaidressingcuisine.com', 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/medina-hospital', 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', 'http://www.starbucks.com/store/14175/', None, '1592858514', 'https://www.hyatt.com/en-US/hotel/arizona/andaz-scottsdale-resort-and-bungalows/phxaz', 'http://www.freshskis.com', 'http://www.burlingtoncoatfactory.com', 'http://locations.harristeeter.com/nc/davidson/268/', None, None, '1592858539', 'http://hustlerhollywoodstores.com/hustler-hollywood-phoenix-arizona', None, None, 'https://www.upack.com', 'http://www.perryspoolpump.com', None, 'http://www.yodipity.com', 'http://www.quicklane.com', 'http://www.theliveryshop.com', 'http://freshrawdogfood.com', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'https://www.dobsonwarnerdentistry.com', 'https://www.concentrix.com', None, 'http://www.lilniblets.com/', None, 'http://optogo.ca', 'http://charlottearrowood.place.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_cltzc_en_homepage_desktop&code=YB', 'http://www.hobbylobby.com/StoreDetail/259/53713', 'https://npavliklaw.com', 'http://www.abovealldriving.ca', 'http://www.blueman.com', 'http://elconaz.com', '1592858621', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281328887&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.frysfood.com', None, 'http://www.homehardware.ca', 'https://www.kingstransfer.com/en/mississauga-movers/', None, '1592858651', None, '1592858659', 'http://www.blinklashandbeauty.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://trca.on.ca/enjoy/locations/claireville-conservation-area.dot', 'http://www.magicofmassage.abmp.com', 'https://gopatterson.com', 'http://mywindowcleanerslv.com', 'http://www.cafeteriaphx.com', 'http://modernmedicallasvegas.com', 'https://www.goodwillaz.org/location/gilbert-ocotillo/#sl62tK85teoKrD2F.97', None, 'http://www.capitalbrewery.com', None, 'http://showmars.com/locations/seventh-street', 'http://www.rentgreenbin.com', None, None, None, 'http://www.azviptransportation.com', 'http://www.truenorthacuwellness.com', None, 'https://www.ReadyRollOffs.com', '1592858739', 'http://dukepubs.ca/richmond/', 'https://www.capriottis.com', 'http://www.specialeventslinens.com', 'http://www.deckerappliance.com', None, '1592858759', '1592858763', 'http://mariscossinaloarestaurant.com', 'http://www.buroakmedicalcenter.com/', None, 'http://palmpalacerestaurant.ca', 'http://www.dominos.ca/', 'http://www.honestplumberinc.com', 'http://totallytifnails.com', None, 'http://www.usairways.com', None, None, 'http://www.charlotteob.org/', 'http://charleys.com', 'https://locations.mrtire.com/oh/avon/38080-colorado-avenue?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'https://www.papajohns.com', 'http://eastcoastcustard.com', 'http://www.rickertandbeaglebooks.com/', 'http://fixitautoclinic.com', None, 'http://www.quiktrip.com', None, None, 'http://www.Danfordgolfinstruction.com', 'http://www.francescasalonandspa.com/', None, 'https://uptownyonge.benefitboutiques.com', 'http://www.loft404.com', 'http://www.worldclass247.com', None, None, 'http://www.soireeslv.com/', 'http://deserthennacompany.com', 'https://www.applebees.com/en/restaurants-lorain-oh/4320-leavitt-road-7612', 'http://thevillageatsunvalley.com/', None, 'http://www.auto-galleria.com', None, 'http://www.cardinalewaymazdalasvegas.com/?ibp-adgroup=yx_target', 'https://www.thalgott.com', 'https://www.orangetheory.com/en-us/locations/texas/westlake/3300-bee-caves-road-200/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.wildgoosebar.ca', 'http://www.lupitasmexicanrestaurant.info/index.html', 'https://www.gerbercollision.com/locations/pittsburgh-prospect-rd-pa', None, None, 'http://www.oakwoodpizzeria.com', 'http://www.desertshowcase.net', 'http://www.lolalashbar.com', None, None, None, 'http://lennar.com/', None, 'http://ilovemyrates.com', None, None, 'http://pizza.dominos.ca/Calgary-Alberta-10108', None, 'http://www.thedaileymethod.com', None, 'http://www.shanghaidumpling.ca', None, 'https://www.usps.com/', 'http://www.JimmyJohns.com', 'http://www.tuesdaymorning.com/index.jsp', 'https://www.napaonline.com', 'http://www.advancedveinaz.com', None, 'https://sellerssportsmed.com', None, None, 'https://skinandmakeupinstitute.com', 'https://locations.panerabread.com/oh/amherst/46402-middle-ridge-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://www.besthomeappliances.com', 'http://www.cherrynailspa.ca', 'https://www.huntington.com/Community/branch-info?locationId=105', 'https://greenvalley.wini.com', 'http://www.twistedherb.com', 'http://www.admtl.com/en/shopping/restaurants/upper-crust/upper-crust-internationale-zone-gate-62', 'http://www.proedgeboxingmma.com', None, 'http://www.upmc.com/locations/hospitals/montefiore/Pages/default.aspx', 'http://thefixDTcoffee.com', 'http://www.dwfriends.org/wordpress/', '1592859049', 'http://www.desertmoonlimos.com', 'http://www.portofsubs.com', None, 'http://centurylink.com/', None, None, None, 'http://www.skydentallasvegas.com', 'http://agracethriftstore.org', 'http://www.vaporrevshop.com', 'http://www.chiropractorshenderson.com', 'http://chandlerdentalhealth.com/', 'https://www.simon.com/mall/the-forum-shops-at-caesars', 'http://www.ctrosesalon.com', 'http://www.mybuildabike.com/', 'http://www.artistcraftsman.com', None, None, None, 'http://neveriachayos.com', 'https://www.shopnorthlake.com', 'http://www.northhillsfamilydental.com', 'https://locator.chase.com/il/peoria/7707-n-knoxville-ave?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.50twenty.com/', None, 'https://www.villageatavonapts.com', 'http://www.happyhookerfish.ca/', None, None, '1592859144', 'https://ad.doubleclick.net/ddm/clk/434331849;236814625;l', None, 'http://www.remixxlv.com/', 'http://totalhomedetail.com/?utm_source=Yelp&utm_campaign=Yelp&utm_content=Yelp%20Ads', 'http://www.gentledentalmillavenue.com/', 'http://www.stpatcc.org', 'http://excellencefootspa.wix.com/89102', None, 'http://www.azallprofloors.com', None, 'http://www.physiciangroupaz.com', 'http://www.schoeppmotors.com/', None, 'http://www.tlcenrichment.com', 'http://www.littlecaesars.com/Locations/tabid/92/location/15106/Default.aspx?id=MTMzNDAwMTE%3d', 'http://www.zolo.ca', 'http://organicare.co', None, 'https://www.searsclean.com/phoenix-az', None, 'http://www.massageaddict.ca/richmondhill', None, 'http://www.greatclips.com/', 'http://www.wwpaintballairsoft.com', 'https://locations.reitmans.com/on-north-york-1266', 'http://kunesstoughton.com', 'http://www.butteravenue.com', 'http://www.pizzapizza.ca', 'http://www.floresfamilydental.com', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', None, 'http://www.RavenIndustriesAZ.com', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl?jp_cmp=rb/LocalListings/aff/branch/na', None, None, 'http://ashleymariehair.com', 'http://www.hayeschiro.net', 'http://www.arizonawigco.com/index.html', 'https://www.sprint.com/storefronts/bd/sprint-avon-oh-44011-d-4684/', 'http://www.wingilariver.com/wild-horse-pass', 'http://knowyourfarms.com', 'https://www.dontortaco.com', 'http://cochiseanimalhospital.com', 'http://cloggedvents.com', 'http://applenailsnspa.com', 'http://www.truecutsalon.com', 'http://www.casago.com/phoenix', 'https://www.sherpaautotransport.com', 'https://locations.tqtire.com/sc/rock-hill/1279-celanese-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.moonvalleydentalcare.com', None, 'http://plomberienormand.ca', None, 'http://www.ferroviaristorante.ca/', 'http://sammysworldsgreatestpizza.com', 'http://www.labcorp.com', 'https://www.walmart.com/store/5257/mesa-az/details', 'https://www.streetfightermotorsports.com', None, 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', 'http://www.italsandwiches.com', None, 'http://www.maidly.net', None, 'https://www.tuftandneedle.com/stores/retail-stores/6a29c2de-ad68-463f-a4aa-147871fa03b2?utm_source=yelp&utm_medium=referral&utm_campaign=gilbert', None, 'http://www.maac.com/texas/austin/colonial-grand-at-ashton-oaks?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://georgetowngoldenfishandchips.weebly.com', 'http://tasteoftoronto.com/', None, 'http://www.tokyosmoke.com', 'http://www.mavistire.com/locations/matthews-nc.asp', 'http://www.jerkynspice.net', None, None, 'https://www.lalocandaaz.com', None, 'http://www.massiveautocollision.com', 'http://local.skechers.com/NV/LAS-VEGAS/126/', None, 'http://massagemaniaglendale.com', 'https://nationwidevision.com/locations', None, None, None, 'https://www.ezflooringanddesign.com', None, 'http://www.athenaspizzaria.com/', None, 'https://www.vonwalterandfunk.com', 'http://www.stacksandyolkslv.com/', 'http://www.burbsbistro.com/', None, 'http://www.AZRealtorShant.com', 'http://www.wellnessforlessmedicalcenter.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://lalacustomcake.com', 'http://www.juniperpoolslv.com', '1592859485', None, 'http://ww3.truevalue.com/mckaystruevalue/Home.aspx', 'https://www.mtoclean.com/scottsdale-az/', 'https://ymcagta.org/find-a-y/toronto-central-grosvenor-street-ymca-centre', 'http://www.JimmyJohns.com', 'http://www.peets.com/coffee.html', 'https://www.digphx.com', 'http://locksmith-henderson.net/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.boilingseafoodus.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1740+West+Highway+160-Fort+Mill-SC-29715/storeid=1571', 'http://www.thebuddhasbazaar.com/', None, 'https://www.prestigeconcreteinc.com', 'https://www.kumon.com/SPRING-VALLEY-EAST-NV', 'http://www.certifiedluxuryauto.com', None, 'http://www.ppmglobal-properties.com/20/Home.html', 'http://www.duncanedward.com', None, 'https://valleyofthesunaz.com', 'http://caribbeancabana.ca', None, None, 'http://www.theclubmonroeville.com', 'http://www.perfectfittailor.com', 'https://lachingada.ca', None, 'http://thunderbirdcollections.com', None, 'https://nevadapilb.glsuite.us', 'http://lushbouquet.com', None, 'http://www.lakesuites.com', 'http://www.nataliepittman.com', 'https://www.closetbox.com/locations/phoenix?utm_content=yelp-listing&utm_medium=directory&utm_source=yelp', 'http://www.greatclips.com/', None, None, 'http://www.1992sharetea.com', 'http://www.bridgesonfirst.com', 'http://www.2youcarcare.com', 'http://stripperbarlasvegas.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.prestigenailboutique.com', 'http://www.zippyicecompany.com', 'https://www.ihop.com/en/menu/?utm_source=CP&utm_medium=CU-GEN-LO-NA-NA-NA-YELP&utm_campaign=LRU', '1592859663', None, '1592859670', 'https://mydeluxecleaners.com', None, 'http://skinblissaz.com/', 'http://www.imsorthopedics.com', '1592859685', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592859699', 'https://www.anytimefitness.com/gyms/2810/Glendale-AZ-85304/?utm_source=yelp&utm_medium=local', None, None, 'http://www.levinfurniture.com/furniture-store/pa/pittsburgh/5846-forbes-ave', 'http://www.gottagetagroomer.com', 'http://www.JusFruit.ca', 'http://www.bunnystavern.com', None, None, None, 'http://www.mybroadwaymodern.com', 'http://www.hootersarizona.com', 'http://furybrewingcompany.com', None, 'https://www.ealocksmith.com', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.maids2nv.com', None, 'http://www.lightbrothersmoving.com', 'http://www.oohmami.ca', None, 'http://www.nikkosushibar.net', 'http://www.ferrasauto.com', 'http://www.weidemiller.com', None, None, None, None, 'http://www.heartsonfire.com/', None, 'http://www.nynyhotelcasino.com/restaurants/restaurants_quickbites.aspx', None, None, 'http://www.gennaslounge.com/', 'https://www.riteaid.com/store-details?storeNumber=07097', 'http://www.stanleysecuritysolutions.com', None, '1592859838', 'https://www.bankofamerica.com', 'https://www.metro.ca/en/find-a-grocery/329', 'http://www.leparisbeurre.com', 'https://en.wowair.ca', None, 'http://svpsports.ca/stores/cartwright', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/richmond-hill-c275.html?mcid=iyp:8368400', 'http://www.salonfrontcenter.com', 'http://paintingwithcanvas.com', 'http://www.woodsidegc.com', None, 'http://www.metropizza.com', None, 'http://delightcleaners.com/', 'http://kens-laundromat.business.site', 'http://www.polishroom.com', 'https://nonitnoggins.com', 'https://www.getpreloved.com', 'http://www.wearephoenicia.com', 'http://www.neechis.com/', 'http://www.mrosmow.com/', 'https://locations.dennys.com/AZ/GILBERT/248832', 'http://www.arizonaballoonsafaris.com/', 'https://www.universalwindowsdirect.com/charlotte', 'https://www.jlautomesa.com', 'http://locator.carolinas.aaa.com/locations/montford/', 'http://www.ctcphx.com', None, 'http://www.mccoyburgerco.ca', 'http://www.hitecvapor.com/default.asp', 'http://www.flipsidedonuts.com', 'http://drnicolecain.com', 'http://www.valleyspinalcare.com/', 'http://meditationcharlotte.org', 'https://www.ziebart.com/?utm_source=Yelp&utm_medium=Profile&utm_campaign=Homepage&utm_term=PA95&CampaignID=YELPprofile', 'https://mintlaserclinic.com', None, 'http://www.gnc.com', None, None, None, None, 'http://www.pizzalinni.ca', 'https://www.queencityanimalhospital.com', None, 'http://www.funkeyoga.com', 'http://www.bellissimoto.com', 'https://handelsicecream.com', 'http://www.pizzapizza.ca/', None, 'http://www.racewaycarwash.com', 'http://www.christyplumbing.com', None, 'http://anthemvillagedentist.com', '1592865765', None, None, 'http://www.lapoblanitanc.com', 'https://www.scissorworksandcompany.com', 'http://valentinorestaurants.com/', 'http://www.robertcromeans.com', 'http://www.everybodylovesfondue.com', 'http://locations.atipt.com/henderson-nv-seven-hills', 'http://www.TheCoreChandler.com', None, None, 'http://aurora.mine-sushi.com/', 'http://www.carnationhomecleaninginc.com', 'http://lamojarralocalv.com', None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'http://www.restathomecare.com', None, 'http://www.doctorsofoptometryinc.com', None, 'http://www.elfishtaco.com/', 'https://www.chazalscottsdale.com', 'http://ironwoodcafe.com', 'https://ad.doubleclick.net/ddm/clk/458685227;262921492;t', '1592865858', 'http://www.phoenixrealtyhomes.com', None, 'http://www.gamestop.com', 'https://sunshine904.wordpress.com', 'http://exhalehealing.com', 'http://www.blackearthvet.com', 'https://atriumhealth.org/locations/south-lake-pediatrics', None, 'http://www.studiorevolution.ca', None, 'http://www.lasvegaswest.minutemanpress.com', None, 'http://www.braidan.com', 'http://www.halstead.ca', 'https://local.fedex.com/pa/pittsburgh/office-2064/', 'http://www.taleriscu.org', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.yakitoribar.ca/', None, 'http://www.dremilyparke.com', 'http://www.sheadoors.com/', None, 'https://www.jasonsdeli.com/restaurants/maryland-pkwy-deli', 'http://surpriseazdentist.com', 'http://www.lifehairstudio.com', 'http://www.ontariocustomglass.com', None, 'https://azairconditioning.com', 'http://www.creativeleather.com', None, None, 'http://kiralasushiandgrill.com/', 'http://tiremartco.com', 'http://www.iheartvape.com', 'http://www.townhomesontheparkapts.com', 'http://www.desertvalleychiropractic.com', 'http://www.toysrus.ca', None, 'http://www.captainsclub.net', 'http://www.platinumtanning.ca', 'http://www.ericalynnmakeup.com', 'http://www.thechesterfieldshop.com', 'https://beefunhotpot.com', 'http://www.managementtrust.com', None, 'http://maxdmaster.com', 'https://www1.shoppersdrugmart.ca', 'https://locations.theupsstore.com/oh/mentor/9401-mentor-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.slapfishrestaurant.com', None, 'https://moundspet.com/locations/middleton/', '1592865990', 'https://www.supercuts.com/locations/nv/north-las-vegas/redrock-commercial-center-haircuts-81949.html', None, 'http://www.eyebrowgenie.ca', 'http://red.nv.gov/Content/Contact/About_Us/', 'http://flowbarbershoplv.wixsite.com/barber', 'http://www.gotransit.com/publicroot/en/travelling/stations.aspx?station=AUGO', 'http://www.facevalues.com', 'https://www.walmart.com/store/5835/cave-creek-az/details', 'http://www.anna-spa.ca/', None, None, None, 'http://kerb.com', 'http://www.tutortime.com/your-local-school/phoenix-az-6086/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://nybride.com', None, 'http://www.stallionmountaingolf.com', 'http://kellereats.com/site', None, 'http://www.KeystoneHomeFinance.com', '1592866040', 'https://www.capriottis.com', 'http://www.davedoesall.com', 'http://www.burritoplace.ca/contact-us', 'http://www.ufoodgrill.com/', None, 'http://www.abcstores.com/www-abcstores-com-72', None, 'http://www.wingmachine.com', 'http://www.yellenchiropractic.com', 'http://www.secondcup.com', 'https://eaglehm.com/arizona?utm_source=yelp&utm_medium=social&utm_campaign=EHM', 'http://magicshoerepairlv.com', None, None, 'https://www.thesterlinggilbert.com', 'http://www.goodwillsp.org/', 'https://scottclarknissanservice.com', None, '1592866087', 'http://www.redat28th.com', 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', 'https://locations.rallys.com/pa/pittsburgh/11749-frankstown-road', 'http://www.golfzonepark.us', 'https://www.spencerstv.com/locations/clearance_center.html?utm_source=Website%20115', 'https://www.humblebeelv.com', None, 'http://www.autospamadison.com', 'http://blissnailbar.com', 'http://www.ljsilvers.com/', '1592866114', 'http://www.arrowstagelines.com', None, 'http://www.azezpawn.com/', '1592866123', 'https://federicosmexicanfood.com', 'http://www.mariecallenders.com/', 'http://www.elanatmallardcreek.com', 'http://www.foodlion.com', 'https://www.jerseymikes.com/9003', None, 'http://www.archerydistrict.com', 'http://www.jocoranglass.com', 'http://www.radair.com/', None, None, 'http://www.qccaninedesign.com', 'https://azbimmermotorwerks.com/mesa-bmw-repair/', None, None, None, 'http://1stchoicemovinglv.com', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/mississauga-2191-dundas-street-e.aspx', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://berylspepperpot.com/locations/toronto-store', 'http://www.selrestaurant.com', 'http://www.barbcpa.com', 'http://landing1.allmysons.com/index.aspx?Ref=phoenix&Src=Yelp', 'https://www.nhwaxhawfamilyandsportsmedicine.org', 'http://www.homedepot.ca', 'http://upscaleaquaticsnc.com', 'https://www.lumazelights.com/pittsburgh-christmas/', 'http://peoplefood.ca/', 'http://lvmis.com', 'https://www.oakcresttavernmadison.com', 'http://www.orbitelcom.com', 'https://locations.massageenvy.com/pennsylvania/wexford/1500-village-run-rd.html', 'http://www.avanti-apts.com', 'http://www.octopuscarwashes.com', None, 'https://www.southwest.com', 'https://www.nvisioncenters.com/locations/las-vegas/nevada-eye-care-east/?utm_source=directory&utm_medium=yelp', None, 'http://www.champaigndentalgroup.com', 'http://metrovino.com/', None, 'https://www.ars.com/pittsburgh', 'http://www.ntitraining.com', 'http://nepalikitchen.weebly.com/', 'http://themillbarandgrill.ca/', 'http://jenniferandresalon.com', 'http://www.arizona.wish.org', None, 'http://www.kevajuice.com/', 'http://www.7-eleven.com/?yelp=22886', 'http://dogsvilleinc.ca', 'http://www.timhortons.com/', 'http://medicaldermatologyspecialists.com/', '1592866247', 'https://www.mark-taylor.com/arizona/san-palmilla/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', None, None, None, None, 'http://www.thegrillonfulton.com', 'http://www.cropbistro.com', 'http://www.shaganappi.com', 'http://www.selahsalonlakewood.com', None, 'http://journeydanceacademy.com', 'http://www.danbradleyglasslv.com', None, 'http://redmaplemassage.com/', 'http://www.topapplianceaz.com', 'http://www.avis.com', None, 'https://www.lashmenow.com', None, 'http://www.jackshouseofflowers.com/?srccode=yelp_track', 'http://www.one-illinois.com', 'http://www.abccountry.ca/', 'https://www.southernair.com', 'http://www.theviewathorizonridge.com', None, 'http://www.mateoshoes.com', 'http://www.hocheeoh.com', 'http://www.metrohealth.org//Middleburg', 'http://shear-perfection-salon-beauty-salon.business.site', None, None, 'http://www.thetreefarm.net', 'https://www.americasbest.com/store-list/desert-sky-az-85033/', 'http://sullivanservice.com', None, None, 'http://Www.sprucegoosejewelry.com', 'http://www.heartcenterofnv.com', None, None, '1592866342', 'http://www.valleyradiologists.com', 'http://mrjohnskitchen.com', None, None, None, 'http://theshmooz.ca', 'https://www.myodetox.com/location/canada/toronto/davisville', 'http://dbcc.com', None, 'https://www.servicemasterclean.com/locations/nv/las-vegas/servicemaster-by-al-3817', 'http://www.stormsrestaurant.com', 'http://www.rossstores.com/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FLASNW', 'https://www.bannerhealth.com/locations/mesa/banner-baywood-medical-center', 'http://levilla.ca/fourth/#top', 'http://www.shannondayrealty.com', 'http://www.sixpennkitchen.com/', 'http://hindolaw.com', 'http://www.blisscupcakes.com/', None, 'http://www.browndermatology.com/', None, 'https://www.opticgallerylasvegas.com', 'http://www.toysrus.com/family/index.jsp?categoryId=2255956&camp=MISC:yelp:store:page:tru:111910', 'http://painfreenevada.com', None, 'http://www.thefreshteashop.ca', None, None, 'http://torontowatchrepair.ca', 'http://REDEMPTIONFitness.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://freshco.com/stores/kingston-road-whites/', 'http://crabandmermaid.com', None, 'http://bigalsdiner.ca/', 'http://www.eastvalleyoralsurgery.com/', None, None, 'http://locations.scrubsandbeyond.com/nv/las-vegas/9839-s-eastern-ave.html', 'http://adfarm.mediaplex.com/ad/ck/24347-208272-18214-4', 'http://www.zacksfireice.com/', 'http://www.cannalilycatering.com', 'http://www.starbucks.com/store/9298/', '1592866450', 'http://www.theflowermerchant.ca', None, 'http://ollivers.com', None, 'http://southparkeats.com', None, 'https://www.peterpiperpizza.com/locations/surprise-az/bell-rh-johnson', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'https://www.theinteriorpainter.com', 'https://www.elysiuminkbodyart.com', 'http://www.starbucks.com/store/11823/', 'https://milaninstitute.edu/campus-locations/milan-institute/las-vegas-nevada-campus/?utm_source=Yelp&utm_medium=CPC', 'https://annieforest.com', 'http://amazingdonuts.com', 'http://www.garage-east.com', None, 'https://www.affordablegaragedoor.biz', 'http://www.fastandgreen.net/', None, 'http://www.bigazpromotions.com', None, 'http://www.arboretumfamilydentistry.com', 'http://www.deltaco.com', 'http://www.soliaspa.com', 'https://www.walgreens.com/locator/walgreens-2363+s+lindsay+rd-gilbert-az-85295/id=5215', None, None, 'http://www.mariosnorthroyalton.com', 'https://www.seasons52.com/locations/az/phoenix/phoenix/4517?cmpid=br:s52_ag:ie_ch:dry_ca:S52Q121LOCURL_dt:20200609_sn:yelp_gt:phoenix-az-4517_pl:locurl_rd:1017', 'http://www.sincityk9.com', None, 'http://www.elleandeve.ca', 'https://www.ashleyfurniturehomestore.com/furniture-stores/united-states/nc/gastonia/gastonia?cmpid=2016YELP', None, 'https://locations.wendys.com/united-states/oh/elyria/525-cleveland-st.', 'http://www.eagleeyepi-az.com', 'http://www.balancechimassage.com', 'http://www.thephoenician.com/golf', 'https://www.nofrills.ca/store-locator/Rod+%26+Joe%27s+nofrills+%28Kingston+Rd.%29/1346?storeId=1346', 'http://www.universalcarpetcare.com/', 'http://www.dickenspub.ca', None, '1592866556', 'http://www.michaelstefansalon.com', None, None, 'http://perspectivedental.ca', 'https://www.prestonkia.com', 'http://www.pizza-ametro.com', None, None, 'http://www.MandarinaByAvanti.com?utm_campaign=gmbclickthru&utm_medium=gmb&utm_source=google', 'https://encorenailstudio.com', '1592866599', None, 'http://www.hardrock.com/', 'http://www.prochilobros.com/', 'http://www.advancedimagepros.com', 'http://corsosrestaurant.webs.com/', 'http://yelp.com/elite', 'https://www.ceenta.com/locations/university', 'http://www.kleenrite.net', 'http://www.fastserveaz.com', None, 'http://locations.in-n-out.com/146', 'http://patiopicasso.net', None, 'http://www.offleasecarsales.com/', 'http://www.redstarkombucha.com', None, 'http://www.mamanitasbinalot.ca', 'http://www.eyemasters.com', 'http://craigpeck.com', 'https://www.hilton.com/en/hotels/phxgdhx-hampton-phoenix-glendale-peoria/?SEO_id=YELP-HP-PHXGDHX', 'http://www.middletoncycle.net', None, 'http://www.tapworkspub.com', 'http://www.shanestintandclearbra.com', 'http://withoutwalls.tv/', None, None, 'http://www.bk.com', 'http://www.goclubfitness.com/', None, None, None, 'http://ballantynecleaners.com', 'http://www.aminahsorganicskinspa.com', 'http://www.bottomdollarfood.com/', 'http://www.lardonrestaurant.com', None, 'http://northwestarmslv.com', None, 'http://www.luckylins.com', 'http://www.gopretzel.com/', 'http://www.johnnymalloys.com', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=916', 'http://www.vivaphotobooth.com/', None, 'http://www.centuryiiimall.com', None, '1592866776', None, 'http://www.rhapsodielle.com', 'http://www.chrismellon.com', 'https://twomenandatruck.ca/movers/on/midtown-downtown-toronto', 'http://runnerssportsbar.food-places.com', 'https://www.adobemassage.com', 'http://www.sohobargrill.com', 'http://www.snapfitness.com/torontohighpark', 'http://www.fivebelow.com', None, 'http://blitzfacialbar.com/location-leslieville/', 'http://www.makeupartistrybynatalie.com', None, 'http://www.maccosmetics.com', 'https://www.famousfootwear.com/?partnerid=YELP', 'http://stationcreek.clublink.ca/', 'http://belacoopanimalhospital.com/', 'http://www.axisemployment.com', 'http://glenmoreaudi.com', None, None, 'http://www.pizzapizza.ca', None, 'http://www.skymarkeyeclinic.com', 'http://www.MrShineExpress.com', None, None, 'http://www.pawsitivepup.com', 'http://www.thebay.com', 'http://www.chewyboba.com', 'http://www.premier-aesthetics.com', None, '1592866886', 'http://www.tunerworks.com', 'http://www.autowhispereraz.com/', '1592866897', 'http://www.platosclosetoakville.com', None, 'http://www.capitalhypnosiscenter.com/', None, None, 'http://barbsbakery.com/', 'http://furrybeginnings.com/', 'http://arkanbarber.com', None, 'http://www.auntieemsminiatures.com', None, 'http://locations.jambajuice.com/ll/US/AZ/Peoria/7369-West-Bell-Rd*-#2', 'http://www.assclownbrewing.com', 'http://www.huntersville.thegreatframeup.com', 'http://www.horizonhobby.com', 'https://www.a1chesney.com/?utm_source=Yelp&utm_medium=ppc&utm_campaign=PinDot', None, 'http://www.millpond-apartments.com', None, 'http://www.bohemiaresto.ca', 'https://www.goodmandentalcenter.com', 'http://mellowmushroom.com/store/az-phoenix-2490-w-happy-valley-rd-85085/?utm_source=Yelp&utm_medium=Organic&utm_campaign=MMWebsite', 'http://www.7-eleven.com/?yelp=32602', 'http://www.cadrerestaurant.com', 'http://www.antoniospizza.net', 'http://www.phoenixpawns.com', 'http://www.summitmedpeds.com', 'http://salonrosalina.com', 'http://www.chefkas.com/fitness-kitchen.htm', 'https://www.discounttire.com/store/nc/gastonia/s/1428?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.harrahs.com/EventsDetail.do?detailName=bette-midler-detail&locationCode=CLV&eventTitle=BETTE+MIDLER', 'http://www.sukhothaifood.ca/parliament/', None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.waylaydesign.com', None, None, 'http://www.glauserwilliamsorthodontics.com', None, None, None, 'http://www.longos.com', 'http://www.watersportsscuba.com', 'http://www.convergence-continuum.org', 'http://www.strumuniversity.com', '1592867057', None, None, 'http://www.greatbunsbakery.net/', None, 'https://mariscos-el-paraiso-de-sinaloa.business.site', 'http://www.elwoodandtherabbit.com', 'http://www.unclerayskis.com', 'http://www.odysseyvetcare.com', 'https://www.ethanallen.com/on/demandware.store/Sites-ethanallen-us-Site/en_US/Stores-Details?StoreID=509&utm_source=yelp&utm_medium=organic&utm_campaign=unpaid_listing&utm_term=509', '1592867089', None, None, 'http://thecrackedegglv.com', 'http://www.livefastcycles.com', 'https://www.nandos.ca', 'http://www.spoonerphysicaltherapy.com/Peoria.html', 'http://www.arleospizza.com', 'http://advancedspinalrehabandwellnesscenter.com', '1592867118', '1592867122', 'http://www.ubreakifix.com/locations/phoenix', 'http://arizonabrazilianjiujitsu.com/?doing_wp_cron=1457928239.4910519123077392578125', 'http://www.iamthelocal.com/', 'http://www.leelaecospa.com', 'http://liveatnoria.com', None, None, 'http://www.crestedduck.com/', 'http://www.goasa.org', 'https://4daughterselectric.com', 'http://portcreditcomedy.com', 'https://www.wellsfargo.com', None, 'http://www.bestmatt.com/', 'http://arizonaadvanceddermatology.com', 'https://9ersdiner.com', 'http://www.detoursamericanwest.com', None, 'http://www.jiffylube.com', None, None, 'http://www.dinardosmansion.ca', 'http://michaelgjonesdds.com', 'http://www.marks.com', '1592867208', 'http://www.mustardmuseum.com', 'http://www.laestancianursingandrehab.com', 'https://churngetsme.com', 'http://www.houseofcarscalgary.com/', 'http://indianbreadbar.com/home', 'https://locations.theupsstore.com/wa/monroe/14751-n-kelsey-st?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.eyeopia.com', None, 'http://www.sharpnit.net', 'http://www.canadiantire.ca/en/store-locator/ab/calgary-south-ab.store.html', None, None, 'http://www.xpresscuts.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://leesilsby.com', 'http://www.animalelegance.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, 'http://www.lkqcorp.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.arbys.com', 'http://www.todayspoolservice.com', None, 'http://www.bondurant.com', 'https://www.24hourfitness.com/gyms/north-las-vegas-nv/north-las-vegas-active', 'https://locations.dignityhealth.org/emergency-room-at-arizona-general-hospital-glendale-camelback-glendale-az', None, 'https://americanmale.com/las-vegas/', 'http://www.starbucks.com/store/9334/', 'https://www.petsuppliesplus.com/Store/OH/Medina/Medina/92?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'http://www.progracedentistry.com', None, None, 'http://sweettomatoes.com', None, 'http://www.ianabakery.com/', 'http://peopleofearthshop.com', 'http://ossalon.com', 'http://www.miboxwest.com/', '1592867354', None, 'http://www.hashhouseagogo.com', 'http://www.experienceseuss.com', 'http://www.starbucks.com/store/7917/', None, None, 'https://www.alaskausa.org', 'http://locations.arbys.com/us/az/sun-city/17032-n-99-ave.html', None, 'https://www.target.com/sl/aurora-west/1413', 'https://calibercollision.com/locate-a-caliber-collision-center/litchfield-park', 'http://scottsdalehairextension.com', None, 'http://www.roadrangerusa.com', 'http://Www.vegassportsandhockey.com', 'http://www.reckerselfstorage.com', 'http://www.scottsdalepsychiatrist.net', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://lstudiosalon.com', 'http://communitytirepros.com/tires-auto-repair-5-phoenix-az', 'http://www.portofsubs.com', None, 'http://www.cassandras.org', 'http://www.templebaraz.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'https://gymvmt.com', 'http://www.littlecaesars.com', None, 'http://glendaleaz.com/', 'https://toujoursmikes.ca/toujours-mikes-kirkland', 'http://copperstatelock.com', None, 'https://www.tommyguns.com/ca/location/calgary-southcentre-mall/', '1592867483', 'http://www.aliantegaming.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://sitaraloungelv.com/', 'http://popeyeschicken.ca/', 'http://www.firehousesubs.com/?ref=yelp', 'http://www.therollingpin.ca', 'http://www.indigovalley.org', 'http://www.discountautorepairlv.com', 'http://www.jumpandshout.com', 'http://www.burnsdentistry.com/', 'http://righthandinc.com/', None, 'https://hawaiianexperiencespa.com', 'http://www.blinemovers.com', 'http://www.premierelv.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.fastsigns.com/88-glendale-milwaukee-wi?utm_source=google&utm_medium=local&utm_campaign=localmaps&utm_content=88', 'https://locations.wendys.com/united-states/mo/rock-hill/9604-manchester-road', 'http://cornercafeaz.com', None, 'http://gonielsens.com/', None, None, 'http://www.baselinevet.com', None, None, 'http://foodfest.51.ca', 'http://www.goldwaterbrewing.com/scottsdale', 'http://www.pieceofthepast.com', 'https://www.buggtreecare.com', None, 'http://www.teashop168.ca', 'http://www.casciomotors.com', None, 'http://www.nevadajobconnect.com', 'http://www.edsfineimports.com/', 'http://www.PartyBusCanada.com', None, 'http://www.marbleslab.ca', 'http://www.usautobodyandpaint.com/home.html', None, None, 'http://www.fadascooters.com/', 'http://knitone.biz', None, 'http://www.paparonisrestaurant.com', None, 'http://www.tomandchee.com', None, 'https://www.cubesmart.com/arizona-self-storage/phoenix-self-storage/72.html?utm_source=yelp&utm_medium=ccpc&utm_campaign=ppct', 'https://www.usps.com/', 'http://www.cheeseburgerinparadise.com/', 'http://www.yumyumbanhmi.com', 'http://www.shalimardesigns.com', None, 'https://www.goodyearsmokeshop.com', 'http://www.mikesautoshack.com', 'http://www.adobeac.com', 'http://jwilsonrealestate.com', 'http://www.uwcu.org/', 'http://www.loblaws.ca/', None, 'http://www.thecaptainsboil.com?utm_source=Yelp&utm_medium=Click&utm_campaign=ON_5313Yonge&utm_content=mainlink', None, 'https://www.papercraneshealthcare.com', 'http://www.marybrowns.com/', 'http://www.campodefiori.ca', None, 'http://www.raesrestaurant.com/', 'http://www.reasonsbanquethall.com', None, None, None, None, 'http://www.carolinascrittersitters.com', None, 'https://www.dillards.com/stores/great-northern-mall-north-olmsted-ohio/0367', '1592867758', None, None, None, 'https://www.wilhelmautomotive.com/locations/goodyear/', None, '1592867777', 'http://www.cityoptical.com', 'http://www.itisadevinebakery.com', None, 'http://staricecreamtoronto.com', None, 'http://www.gihaul.com', 'http://www.646weightliftinggym.com', 'http://www.tempemarketplace.com', 'http://Brothersbakery.ca', 'http://southsidebbqcompany.com/', 'http://www.3rootstempe.com', None, 'http://www.mondashaircare.com', None, 'http://www.enmarflooring.com', None, None, 'http://www.lachaecosmetics.com', 'http://shishkababexpress.ca', 'http://www.thegroceryohc.com', None, None, 'http://www.djmistry.com', None, 'http://www.asahi-sushi.com', 'http://thebeach.systemfitness.ca', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.tribsteakhouse.ca', 'http://www.panerabread.com', None, 'https://arcadiatavern.com', 'https://www.bankofamerica.com', 'http://prodaytrainingcamp.com/', 'https://lvcellcity.net', None, 'https://vcahospitals.com/valley-vet?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Valley_Vet_Animal_Hospital=main_url', None, None, None, 'http://www.fiestamexrest.com', 'http://lunajunction.ca', None, 'http://www.davispoolservice.com/', None, None, None, 'http://www.paradisefoundtours.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.CompassionateAssistance.com', None, 'http://www.hq-law.com', 'http://Worstshowinvegas.com', None, 'http://www.tenpinalleys.com', None, 'http://www.prada.com/en/store-locator.html?shop=13', 'http://flo-proplumbing.com/', 'http://www.bettenhauscanada.com', 'http://www.waxcenter.com/oh-fairview-park?utm_source=yelp&utm_medium=cpc&utm_campaign=fxtxiTdvCNTQq9XhcCU_iA', 'http://www.napaautopro.com/auto-repair/alberta/calgary-a-r-autopro/', None, None, 'http://kangarootickets.com', 'http://www.azmattressoutlet.com', None, 'http://whitecastle.com', 'http://www.tintqueensway.com', 'http://www.sanangelinapts.com/', 'https://www.chilis.com', None, 'http://locator.carolinas.aaa.com/locations/albemarle-road/', 'https://www.nonns.com', 'http://www.dragonstrongsville.com', 'http://www.franklloydwright.org/taliesin-west/tickets-and-tours.html', 'http://www.bobbeeosbbq.com', 'http://www.stubbechocolates.com/', 'https://www.VegasIndoorSkydiving.com', 'http://www.touchdownsportswear.com', 'http://www.TheCanineClubDaycare.com', 'http://www.haagendazs.us/shops', 'http://Artisticrefacing.com', 'http://www.treats.com', 'http://schools.ccsd.net/goolsby/', 'https://www.get-go.com/', 'http://www.husbandandwifelawteam.com', 'http://locations.harristeeter.com/nc/indian-trail/129/', 'https://stores.nordstromrack.com/us/az/phoenix/2073-east-camelback-road?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=367&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', 'http://www.carolinaecigs.com', 'http://www.momdocwfw.com/tempe', 'http://fitnessfor10.com/locations/nevada/las-vegas/', 'https://www.choicehotels.com/arizona/fountain-hills/comfort-inn-hotels/az014/rates', None, 'https://coyotetire.com', 'http://bobandsheri.com', None, None, None, 'http://www.musicologyaz.com/', 'https://www.stationcasinoslive.com/sunset-station/?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'https://www.hubbardswim.com', 'https://nathansfamous.com/restaurants/luxorhotelcasino-lasvegas-130416/', 'https://www.brightstarcare.com/charlotte-s', 'http://knockout-fitness.com/locations/paradise-valley/', None, None, 'https://www.urbanoutfitters.com/stores/camelback', 'http://www.londonbarbers.ca', None, None, 'http://www.lilporgysbbq.com', 'http://www.riderscycleboard.com', 'http://www.furrypawsmobilegrooming.com', 'http://www.vecchiofrak.com/', None, 'http://www.bk.com', 'http://www.lephodtlv.com', 'http://shopnsavefood.com', 'http://www.waterworkspoolsaz.com', 'http://atropicalconcept.com', None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-saguaro?utm_source=yelp&utm_medium=local&utm_campaign=Honorhealth_Medical_Group_Saguaro', '1592868194', 'http://potato-barn.com/', 'https://www.pizzahut.ca/store-details/store-R42101/pizza-hut-Etobicoke', 'http://jaythomascarlson.com', 'http://www.brooksentertainment.com', 'http://www.barnovaavon.com', 'http://qualitystarimports.com', 'http://www.thecandyland.ca', 'https://azurevillas.mgproperties.com', 'http://www.soletherapybyglenda.com', 'http://www.autotransteam.com', 'https://www.usps.com/', 'http://www.sushinbento.com', None, 'https://www.bellagio.com/en/entertainment/o-by-cirque-du-soleil.html', None, 'http://www.delrentals.com', 'http://michael-angelos-bakery.myshopify.com/', 'https://www.caesars.com/planet-hollywood?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=PlanetHollywood&utm_content=hotel', 'http://sandoozles.ca/', 'http://azsonspainting.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://thenailsalonspa.ca', '1592868276', 'http://www.sushibrokers.com/', 'http://www.bigelowblvddetail.com', 'http://www.lavaporsclt.com', None, 'http://www.racewildhorse.net', 'http://www.yogashalacalgary.com', 'http://www.blazingsaddlecleveland.com/', 'http://millenniumalarmsystemslasvegas.com', 'http://www.musiclessonsarizona.com', 'http://www.thetexaslonghorn.ca', None, None, None, 'https://agents.farmers.com/nv/las-vegas/birant-or?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.nailsaloninchandler.com', 'http://www.wingsandaprayer.wordpress.com', 'http://www.stuffingtonbear.com/', 'http://www.jaliscoauto.com/home', None, 'http://survivethenight.ca/', None, 'http://www.cheesecakecafe.ca', 'http://www.clubreefaz.com', None, 'http://www.reserveatkentonplace.com', None, 'http://www.sunchevy.com', 'http://qoola.com', 'http://fratellos.net/', 'http://healthspalv.com', None, 'https://linktr.ee/neeziiebabiiebeauty', 'http://www.ceremonyofdreams.com', 'http://www.avella.com/avella-scottsdale', None, None, 'http://www.whatsbuggingyounevada.com', None, 'http://www.selectglass.com', 'https://locations.wendys.com/united-states/oh/mayfield-heights/1374-som-center', 'http://www.energycrew.ca', 'http://www.azdavismovers.com', 'https://www.petittigardencenter.com/index.php/locations/oakwood-village', 'http://www.quiksilver.com', None, 'https://www.bjs.com/cl/warrensville-heights/0122', 'http://www.taylortire.ca', '1592868433', 'http://www.omegadogtraining.com', 'http://www.dairyqueen.com', 'http://meineke.com', 'https://anevasolar.com', 'https://www.rubytuesday.com/', None, 'http://www.dustingdivasinc.com/', None, 'http://www.auburnveterinaryhospital.com', 'http://arizonaoncology.com/locations-physicians/physicians/profile-dennis-r-scribner-jr-md-facog-facs', 'https://www.drshier.com', 'http://www.coyotescafecantina.com', None, 'http://fitness.reebok.com/store-locator/', None, None, 'http://www.pvfamilycare.com', 'http://www.crazyshirts.com', 'https://www.mypetmarket.com', 'http://www.paintwithprecision.com', 'http://www.woodsideaptliving.com', 'http://theendvegas.com', 'https://www.centennialhillshospital.com/?utm_medium=referral&utm_source=yelp', 'https://nuvonails3.business.site', 'http://www.indiafestival.net/', None, 'https://www.scottsdalelaserengraving.com', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://avondalecleaners.net/', 'http://ohashisushi.wordpress.com/', None, None, 'https://www.dlgteam.com/downtown-las-vegas/', 'http://yummycone.ca', 'http://allergenuityhealth.com', None, 'http://www.dosummers.com', 'http://www.elysianskinbeauty.com', 'http://aquitaineauto.ca', 'http://www.3riversvw.com', None, 'http://danecountyfamilyacupuncture.com', 'http://www.almaimports.com/', 'http://SaharaBehavioralHealth.com', 'https://www.ewingirrigation.com/locations/index/branch/id/280/', 'http://snappy-lawnservice.com/', 'http://www.salvationarmysouthernnevada.org', 'https://www.canyonstateroofs.com', 'http://www.guaranteeddoor.com', 'http://www.3rdfloortailors.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, None, 'http://www.meltingpot.com/fairviewpark-rockyriver/welcome', 'http://speedysvapes.com', 'https://mindsparkescape.com/tempe?utm_medium=websiteclick&utm_source=yelp', 'http://www.chocolatierbarrucand.com/', '1592868631', 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', None, None, 'https://locations.jackinthebox.com/us/az/mesa/525-n-stapley-dr', 'http://centaurgalleries.com', 'http://www.olanmills.com', 'http://www.efreshmeals.ca', 'http://www.quinta.ca', 'http://www.thejasongeorge.ca/', 'http://atomicpestcontrol.com', 'http://www.56northapts.com/', None, 'https://melrosevintagemarket.com', 'http://www.terribleherbst.com/', '1592868688', None, 'http://pedalinx.com', None, None, 'https://www.sinclairoil.com/location/lv-7-mart', 'http://www.doggonecrazykennels.com', 'http://www.brueggers.com/', 'http://elizahotelindigo.com', 'http://www.jodymaroni.com', 'http://www.z.boutique', None, None, 'http://conquerbootcamp.ca', 'https://www.skinvitality.ca/?src=yelp', 'http://www.green-rice.com', 'http://www.creativeleather.com/', 'https://vmts.com/locations/raintree-drive-scottsdale', 'https://www.minto.com/gta/Toronto-apartment-rentals/Minto-Yorkville/main.html', 'https://www.missionpalmshealthandrehab.com', None, 'https://soup-dujour.business.site', 'http://www.wingwarehouse.com/', 'http://www.blueberryjewelers.com', None, 'https://locations.captainds.com/ll/US/NC/Charlotte/2838-Freedom-Dr', '1592868775', '1592868778', None, 'http://www.eliteautoaz.com', 'http://www.littlecaesars.com', 'http://www.stclairicecream.ca/index.html', 'http://communitymatterscafe.com', None, None, 'http://www.desertspineandsports.com/', 'https://foxcigarbar.com/gilbert/', 'http://www.salemdds.com', None, 'https://www.longhornsteakhouse.com/locations/oh/medina/medina/5138?cmpid=br:lh_ag:ie_ch:dry_ca:LHQ121LOCURL_dt:20200619_sn:yelp_gt:medina-oh-5138_pl:locurl_rd:1101', 'http://680bins.wixsite.com/waste-management-bin', 'http://www.benkovitzseafood.com', '1592868830', 'http://www.miamibeachgrill.ca', 'http://www.cbdmesa.com', None, 'http://www.thelightsjuicery.com', 'http://www.cambodicankitchen.com/', 'http://www.generationrestaurantsupply.com/', 'http://www.6ycle.com', 'http://www.mmgyn.com', None, 'http://twfmlasvegas.com', None, 'http://www.highsidebar.com', 'http://www.thesuperiorinsurance.com', None, 'http://www.ourtowncinemas.com', None, 'http://www.floralmagic.net/', 'https://www.gianteagle.com/Stores/Store/?storeId=218', None, 'http://www.volvounionville.com/?lng=2', None, None, None, 'http://www.brightnow.com/locations/dental-office/glendale/bright-now-dental/40070?utm_campaign=local_profiles&utm_medium=profiles&utm_source=yelp', 'http://lacatrinamexicangrill.com/', 'http://www.mypermanentmakeupaz.com/', None, 'http://www.illinihillel.org', None, None, 'http://www.arizonagreencleaning.com', None, None, 'http://eklecticpie.com', 'http://www.jimsmotorsaz.com', None, 'http://www.yorkvillesmiles.com', 'http://www.petco.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'https://locations.thecheesecakefactory.com/oh/westlake-93.html', 'https://www.lincolntech.edu/campus/las-vegas-summerlin-nv', 'http://sandyaleksander.ca', 'http://capstoneroofingaz.com/', 'https://www.getgocafe.com/store/details?name=edgewood-getgo', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.studio-616.com', None, 'http://www.dornhardware.com/', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85019/7111-near-winton-heights/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-7111&utm_content=website-link&howheard=IYE', None, 'http://bistronarra.com/', 'https://bostonmarket.com/?utm_content=web%C3%8A&utm_medium=app&utm_source=yelp', 'http://www.countryclubatthemeadows.com?rcstdid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.littleartika.com', 'https://www.daybreakgardensapts.com', 'http://learningworkspreschool.com', 'http://www.concentra.com', 'http://acservicerepairphoenix.com', None, 'http://www.johnsonwindows.com', 'https://www.walmart.com/store/387/chandler-ok/whats-new', 'http://www.dignitymemorial.com/funeral-homes/toronto-on/rosar-morrison-funeral-home-chapel/3155', None, 'http://scratchmadestjoe.com', 'https://www.extraspace.com/storage/facilities/us/north_carolina/huntersville/1000001181/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.candyscostumeshoponline.com', 'http://www.jagplumbing.ca', 'http://cafecoda.club', 'https://www.kevinortaledds.com', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.imperialtileandmarble.com', 'http://bosadonutsaz.com', None, 'http://www.wirelesstoyz.com', None, 'http://www.applecookies.com/', 'http://www.peppermintforest.com', 'https://www.storagewest.com/facilities/buffalo-drive/?utm_medium=organic&utm_campaign=yext&utm_source=yelp', None, 'http://www.blinsonair.com', None, None, 'http://www.dallmanplumbing.com', None, 'https://researchforlife.org', 'http://www.michaelkors.com', 'http://www.thepieplace.net', None, 'http://hiltongardeninn3.hilton.com/en/hotels/nevada/hilton-garden-inn-las-vegas-city-center-LASLGGI/index.html?SEO_id=YELP-GI-LASLGGI', 'http://tnah.ca/', None, 'http://www.iphotoshop.com', None, 'http://www.atouchofeuropeancafe.com/', 'http://www.omegaradon.com', 'http://www.haul-my-mess.com', 'http://wcinjurylawyers.com/', 'http://theclevelandvet.com', None, 'http://www.bojangles.com', None, 'http://www.wholesomefoodsusa.com', None, 'http://www.dornhardware.com/', '1592869207', None, 'http://www.swintonsart.com', 'http://www.timothys.ca', 'http://www.illinilandscaping.com', None, 'http://www.drryanmitchell.com', None, 'http://www.planet21salon.com/location/the-arboretum/', 'https://www.chick-fil-a.com/scottsdale101', None, 'http://dbackpools.com/', 'http://collegecurrencyinvestments.com', None, 'http://www.opensesamegaragedoorslv.com', 'http://www.gssfinc.com', 'http://www.thirstygoatbrew.com', 'http://www.retreatattheraven.com', None, None, 'http://www.luxorcafe.ca/', None, None, None, 'http://www.fitnessworks.com/', 'http://www.devanmanagement.com', '1592923262', 'http://www.euromotorsports.ca', 'https://www.fetchpetcare.com/pittsburgh-cranberry-wexford', 'https://magalbbqlv.weebly.com', 'https://www.southerncarcompany.com', 'http://www.photobangbang.com', 'http://baogong.business.site', 'http://www.ciaaz.com', 'http://northhavenbarbershop.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.equilibriumfurnishings.com', 'http://www.richfieldautocenter.com', 'http://www.98kupd.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://scottsdaleboxingclub.com', 'http://www.germanautowerkslimited.com/', 'http://www.hairartisans.ca', None, 'http://www.bellawomenscare.com', 'http://www.lvwheel.com', 'http://www.ivysdiaperservice.com', None, 'https://fivedollarfoodfest.com', None, None, None, '1592923345', 'http://www.betterthannewlv.com', 'http://www.mauritianpot.ca', 'http://www.uphillwireless.com', 'http://www.marys-restaurants.com', 'http://www.cpk.com/location/details/Fashion-Show-Mall', 'http://twinpediatrics.com/', 'http://www.valleyymca.org/scottsdale', None, 'http://www.lagerandvine.com', 'http://www.BadAzzBBQ.com', 'https://www.foutzdental.com', 'http://prolocksmithhenderson.com', None, 'http://www.universityinntempe.com', 'http://www.ubreakifix.com/locations/charlotte/', None, 'https://www.walmart.com/store/4356/las-vegas-nv/details', 'http://www.hamptoncommunitylibrary.org', 'http://www.dominicsfamousdeli.com/', 'http://www.yogurtys.com/', 'https://www.mecknc.gov/parkandrec/parks/parksbyregion/centralregion/pages/independencepark.aspx', 'http://www.dream-kitchens.com', 'https://mygreatlakes.org', None, 'http://leesliquorlv.com/locations/lake-mead-tenaya-2/', None, 'http://www.karakakes.com', 'http://renumadison.com', 'https://theredgeranium.wixsite.com/website', 'https://www.cfshops.com/shops-at-don-mills.html', 'http://www.geppettos.com', 'http://www.theresellerscloset.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.madisonsfamilywellness.com/', 'http://www.summerlinbodytherapeutics.com/', 'https://www.sarkujapan.com/#home', 'https://order.littlecaesars.com/en-US/stores/32910002/21800-center-ridge-rd/rocky-river/oh/about', 'https://mollymaid.com/east-mesa-apache-junction', 'http://www.catawbabrewing.com', 'http://www.aliciasmobiledogandcatgrooming.com/', 'http://www.howiespizza.ca/', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3034+West+Lincoln+Avenue-Peoria-IL-61604/storeid=7798?cid=ps_ylp_2020', 'http://www.tipofthetailgrooming.com', None, 'https://www.wyndhamhotels.com/hotel/17659?iata=00093785&tel=18003291073&cid=fe:di:20161220:yl:pp:dius:17659', 'http://www.bristledboar.com', None, 'http://www.a2zpestcontrol.net', 'https://www.benjerry.com/universityheights', 'http://grandcentralclothing.com', 'https://locations.massageenvy.com/arizona/mesa/1657-south-dobson-rd.html', None, 'https://locations.wafflehouse.com/nc-charlotte-449', 'https://thebrillline.com', 'https://www.ihealthi.us', None, 'http://www.312opticalstudio.com', None, 'https://zoeskitchen.com/locations/store/az/scottsdale', 'http://www.zanzibartavern.com', 'https://priorityserviceslasvegas.com', 'https://www.partyspizzas.com', 'http://www.marriott.com/hotels/travel/yyzmq-courtyard-mississauga-airport-corporate-centre-west', None, None, 'http://www.drbrendali.com', 'http://www.kirtlandvet.vetsuite.com', None, 'http://www.littlecaesars.ca/Locations/tabid/89/Default.aspx?id=NDg0NDAwMDI%3d&location=L3P+3J3', None, 'http://dignityhealth.org/doctor/WF_FindADoc_Profile.aspx', 'http://www.oasisatgoldspike.com', None, 'http://www.campbowwow.com/las-vegas', 'http://www.bluejaybarbering.com', 'https://www.huntington.com/Community/branch-info?locationId=199', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'https://theinternationalteam.managebuilding.com', 'http://www.harrahs.com/casinos/rio/restaurants-dining/buzios-seafood-restaurant-detail.html', 'http://www.ssl.edu', 'http://bluedonkeystreatery.com/', 'http://wokinbarbecue.com/index.html', None, None, None, None, 'https://stores.dickssportinggoods.com/wi/madison/178/', None, 'http://www.lrkeyebrowthreading.com', None, 'http://www.bridgesandbourbonpgh.com', 'http://lemacaron-us.com/scottsdale-quarter/', 'http://www.ahwatukeeglass.com', None, 'http://www.davinciteethwhiteningsystem.com/', None, 'http://www.canadianfoodservices.com', 'http://www.gandermountain.com/store-locator/details/Twinsburg-OH-305', None, 'http://www.ChildrensChoice.com', None, None, None, 'http://pinkponyscottsdale.com/', None, None, 'https://stores.motherhood.com/s/arizona-mills-outlet-tempe?latitude=33.383125&exclude=15252&page=1&longitude=-111.964485&storesPerPage=3', None, 'http://www.publicworkscoffee.com', 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', 'http://www.sundevilauto.com/locations/az/glendale/glendale-7', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=521', 'https://nathansfamous.com/restaurants/luxorhotelcasino-lasvegas-130416/', None, 'http://brassthelounge.com/', 'https://www.planetfitness.com/gyms/solon-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://theroostertavern.com', None, 'http://baccusrealtygroup.com', 'http://www.urbanautoworkz.com', 'http://kidsrusvegas.com/', 'http://www.smoothwax.ca', 'http://patsautoaz.com/', 'https://dutchbros.com/?utm_source=north-las-vegas&utm_medium=yelp&utm_campaign=website_north-las-vegas', 'http://www.escapejavajoint.com', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', 'http://www.ollies.us', 'http://www.plaza-network.com/', 'http://www.trebellaaz.com', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', None, 'http://www.carolest-pierre.com/', 'http://www.relaxjustvaping.com', 'http://www.pamier-kabob.com/', 'http://www.quiktrip.com/', 'http://www.cynthiafindlay.com', 'http://www.streetsofnewyork.com', None, 'http://www.closemyhome.ca', None, 'https://www.wyndhamhotels.com/hotel/18925?tel=18885953511&iata=00093785&cid=fe:wg:20170523:yl:pp:winus:18925', 'https://craigsplumbing.com', 'http://olenliving.com/communities/arizona/one-north-scottsdale', 'http://www.walkonmeflooring.com', None, 'http://www.goodeggdining.ca', 'http://www.lamagiedelapomme.com/', 'http://www.treasurehuntcoins.com', 'https://www.tidedrycleanersaz.com/locations/alma-school', 'http://www.kenputerguru.com', 'http://www.giostire.com', None, 'http://www.mocacleveland.org', None, 'http://qdoba.com', 'http://myaccount.srpnet.com/paymentlocations/', 'http://www.visitingangels.com/vegas/home', None, None, 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', None, 'http://www.customcalipers.com/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.flooringrockyriveroh.com', 'http://crepeshacklv.com', 'http://www.woodlandsusa.com/', 'http://www.tpc.com/scottsdale', 'http://thelocaldonutshop.com', 'http://browsthreadingsalons.com', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.meatballz.net', '1592923820', 'https://www.exhalebrands.com', '1592923825', 'http://www.concordialm.org/locations/concordia-of-the-south-hills', 'https://locations.wendys.com/united-states/az/chandler/1045-s.-arizona-ave', 'http://www.prettyinthecity.ca', 'https://locations.sonicdrivein.com/az/glendale/13751-west-glendale-avenue.html', 'http://www.homeconceptscustomremodeling.com', 'https://www.dalesheating.com', 'http://www.araair.com/', None, 'http://tshirtdinervegas.com', 'https://www.tempesmiledesign.com', 'http://topnailssalonchampaign.com', 'http://www.nouveaubistro.com', 'http://thecomputer-er.com/', 'http://www.alphagraphics.com/centers/scottsdale-arizona-us037/index.html', None, 'http://slslasvegas.com/cleo', 'http://azyardscapes.com', 'https://stores.hallmark.com/oh/brooklyn/karens-hallmark-shop-brooklyn-oh-4744.html', None, None, None, 'http://www.exxonmobilstations.com/home.php?c=20140424134755&lang=en-us&storenum=af8bcd077e77bb8ac957507ed31ec51f', 'http://www.popalock.com/franchise/charlotte_nc_locksmith.php', 'http://bonniesbarkery.com/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://www.las-vegas-window-cleaning.com', None, 'http://www.pclaptops.com', None, 'http://Beautifullytwystedsalon.com', 'http://www.rubinsrestaurant.com/index.htm', 'http://www.classicjuice.co', 'https://stores.bestbuy.ca/en-ca/on/north-york/5095-yonge-st-suite-a14', 'http://www.segwaypittsburgh.com', None, 'http://www.coppolacheney.com', 'http://www.starbucks.com/store/11823/', 'http://www.salonkismetaz.com', None, 'http://www.nekomassage.com', None, 'http://Www.lvpaindoc.com', 'http://www.highparkmartialarts.ca', None, 'http://www.foreigncarscharlotte.com', 'http://www.rhinoscleaningservices.com', 'http://www.lat30dining.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://ahipokibowl.com/chandler', 'http://www.cashamerica.com/SUPERPAWN-stores/NV/LASVEGAS/LV12', 'http://www.eatsouthbound.com', 'http://www.johnnyrockets.com/', 'http://www.dlishcupcakes.com', None, 'http://www.bbbsaz.org/site/c.bkLWKhOTLfK2E/b.6561823/k.EEE3/Home_Page.htm', None, 'https://bostonpizza.com/en/locations/sunridge.html', 'http://www.hdoutlets.com', 'http://www.centralebergham.com', 'https://www.tireworks.net/locations/2220-w-horizon-ridge-pkwy-henderson/', None, 'http://www.winewarehousearizona.com/', 'http://www.thecanadianbrewhouse.com', None, None, None, None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'http://www.metrolinaeye.com', None, None, None, 'http://www.lhdentalcare.com/', None, 'http://www.rxbycc.com', 'http://www.jambajuice.com', 'http://www.flowersbyrenee.com/?srccode=yelp_track', None, 'https://smartstopselfstorage.com/storage-locations/usa/nevada/las-vegas/smartstop-self-storage-4851-e-bonanza-rd', None, 'http://www.beautyrex.com/', 'https://stores.libertytravel.com/pa/ross-township/4818-mcknight-rd.html?utm_source=yelp&utm_medium=direct&utm_campaign=evergreen-store-pages-rosstownship-pa', 'http://www.sisenor.org', 'https://www.hendersonhospital.com', None, 'http://www.professionalbeautysalonaz.com', 'http://www.ximenesbjj.com', 'http://www.elementcarpetcleaning.com/', None, None, 'http://www.Alteredstatetextileimaging.com', 'http://makirrito.ca', None, 'https://www.sweye.com/locations/scottsdale-bell-rd/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-scottsdalenorth&utm_content=website', 'http://www.fireflylv.com', None, 'http://www.allstar-materials.com', 'http://www.cartersoshkosh.ca', None, 'https://www.mcdonalds.com/us/en-us/full-menu/123dollarmenu.html?cid=PS:GCM_MOP:NB::Yelp:All', None, 'http://Gamechangerlv.com', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'http://www.chonglawgroup.com', 'http://www.JohnsonRoofingAZ.com', 'http://www.ntb.com/store/8469/clover-sc-29710-3600?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, None, None, 'http://www.esurbanhair.com', None, 'http://arrichion.com', 'http://appliancelove.com/', None, None, 'http://www.marychapmanlaw.com/', None, None, None, 'http://www.bluechipglass.com/', 'https://sites.google.com/site/kneadmeaz/home', 'http://www.milliecreperie.com', 'http://www.suncityazdentist.com/', 'http://stores.sportsauthority.com/az/tempe/sporting-goods-tempe-691.html', None, None, 'http://www.bridalbeginning.com', 'http://oldtimepottery.com', 'http://aldentemarkham.com/#home', None, None, None, None, 'http://www.thevineyardsonlakewylie.com', 'http://www.fastfixjewelers.com', 'http://www.jiffylube.com', 'http://www.landscapelightingconnection.com', '1592924201', None, 'http://www.gioninos.com', '1592924214', None, 'http://www.thiepcuoicali.com', None, 'http://charlotteyouthballet.org', None, 'http://www.JimmyJohns.com', None, 'http://www.pekarabakery.com', None, None, None, None, None, 'https://starbodyvegas.com', None, 'https://www.louisianaffccharlotte.com', 'http://www.kujira.co', 'http://www.freshstartdiner.com', 'http://www.magickeystolearningcdc.com', 'https://www.handandstone.ca/locations/toronto-dan-leckie', 'http://www.emmasallen.com', 'http://www.aeropostale.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4755+West+Ann+Road-North+Las+Vegas-NV-89031/storeid=2989?cid=ps_ylp_2020', 'http://www.Method-Djs.com', 'http://www.wingilariver.com/index.php/vee-quiva-hotel-casino/dining/ditkas-restaurant', None, 'http://www.allamericandjaz.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006430791762&ds_s_kwgid=58700000444978102&ds_url_v=2', 'http://www.candalinabride.com/', 'http://bierportpgh.com', 'http://www.admtl.com/fr/commerces/restaurants/trinity/trinity-zone-domestique-porte-01', 'http://www.verizonwireless.com/b2c/index.html', 'https://www.ihop.com/en/restaurants-phoenix-az/5020-e-ray-rd-1508', 'http://jetsupercleaninc.wixsite.com/mysite', None, None, 'http://www.rumshakers-pgh.com/', 'http://gettapizza.ca', 'http://www.elegancesalon.ca', 'http://www.cakepalace.org', None, 'http://stores.toysrus.com/nc/concord/toy-store-concord-nc-8825.html', 'http://www.orvis.com', '1592924375', 'http://www.gearguardsports.com', 'https://www.sprint.com/storefronts/bd/sprint-glendale-az-85308-fcs-541/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://boatyardeats.com', 'http://www.arizonabridalshow.com', None, 'https://www.lifeway.com/en/store-detail-4826', 'https://www.usps.com/', None, 'https://www.homedepot.com/l/Cleveland-Heights/OH/Cleveland-Heights/44118/3818?cm_mmc=seo-yelp&', 'http://www.theratroomratteryofphoenix.webs.com', 'http://fbipizza.com/', None, 'http://tjmaxx.com/', 'http://www.calgaryhumane.ca', 'http://www.alterationsbyelizabeth.com', None, 'http://arizonaaircleaners.com', 'https://www.mattressfirm.com', None, 'http://www.smithbrosfloors.com', 'http://www.scottsdaleaz.gov/parks/isp.asp', 'https://www.afw.com/stores/az/glendale', None, None, 'http://www.internetkitchenstore.com', 'http://www.mckinnonheating.com', None, 'http://www.capaulschristmastreefarm.com', 'http://www.StyleExchangeBoutique.com', 'http://www.mydesertdental.com', 'http://www.humblebeelv.com', None, 'http://www.oysterboy.ca/', 'https://www.tgifridays.com/locations/1852/fridays-las-vegas-west-nevada', None, 'http://www.paradisefabricsandcostume.com', 'http://www.solup.com', 'http://www.benchmarkinteriorsaz.com', 'https://www.sunnysidemitsubishi.com', None, 'http://www.vivahair.ca', 'http://lunaseadayspa.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.tiredoctornc.com', 'http://24-7motorcoachcollisioncenter.com', 'http://www.cashamerica.com/SUPERPAWN-stores/AZ/PHOENIX/Pho01', None, None, 'https://www.hyatt.com/en-US/hotel/canada/hyatt-regency-toronto/torrt?src=prop_sem_torrt_nb_yelp_tcepilot', None, 'https://doubletree3.hilton.com/en/hotels/nevada/tropicana-las-vegas-a-doubletree-by-hilton-hotel-LASNTDT/index.html?SEO_id=YELP-DT-LASNTDT', 'http://royalashburngolfclub.com/', 'http://www.css-computers.com/', None, 'https://elementsmassage.com/avon-ct', 'http://www.hypoxistudio-ballantyne.com/', 'https://stores.loft.com/us/az/scottsdale/15211-north-kierland-blvd.html', None, None, 'https://www.carstar.ca/en/locations/ab/calgary/carstar-calgary-sunridge-16118/', 'http://lasvegas.carenow.com/location/cheyenne-durango', 'https://www.infinitiofscottsdale.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://cctta.net/', 'http://www.starbucks.com/store/9298/', 'https://www.namisushi.ca', 'https://thaiexpress.ca', 'http://www.bethkeheating.com', None, 'http://www.freshslice.com', None, '1592924614', '1592924618', 'http://www.starbucks.com/', 'http://www.gregorysmarineandrv.com', 'http://vuria.com', None, 'http://www.midasspring.com', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'https://sunsetstation.sclv.com/Gaming/Bingo/?utm_term=SS&utm_content=SS-PROPERTIES&utm_medium=SOCIAL&utm_source=YELP&utm_campaign=SS-YELP', 'https://www.menswearhouse.com/store-locator/2503?utm_source=yelp&utm_medium=listing&utm_content=2503&utm_campaign=AZ', None, 'http://watchit.ca', 'http://www.wix.com/unihealth/centre', 'https://www.bodynbrain.com/glendaleaz', 'https://locations.vitaminshoppe.com/az/phoenix/vitamins-supplements-phoenix-az-210.html', 'http://kopkesgreenhouse.com/', 'http://www.patcatans.com/craft-store-locations/willowick-oh', 'http://www.kikisbakery.net', None, 'http://wentworthfamilydental.com', None, 'http://www.sportgrill101.com', 'http://drakeequipment.com', 'http://www.apcopest.com', '1592924694', 'http://plumberfromdownunder.com', 'http://www.kentofinglewood.com/', 'https://www.lodgeatmallardcreek.com', None, 'https://www.pgatoursuperstore.com/stores/summerlin-nevada/1210.html', None, 'http://www.ChampaignExperts.com', 'http://www.desertrayscafe.com/', 'http://www.eggspectation.ca/', 'http://eatatmenus.com', None, None, 'http://www.fastfixjewelers.com', None, None, None, None, None, 'https://www.optometristwickliffe.com', 'http://www.gelatogelato.ca/', None, None, None, None, None, 'http://www.craigperry.com', 'http://www.dynotune.biz/index.html', 'https://www.mastercuts.com/locations/il/champaign/mastercuts-market-place-mall-haircuts-1403.html', 'http://sopressata.ca/', 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', None, None, None, None, None, 'https://www.petsmart.com/stores/us/nv/las-vegas-store1153.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://www.cookiesbydesign.com/locations/arizona/scottsdale/85250_045.aspx', 'http://www.fivestarmortgagelv.com', None, 'http://www.gwhaz.com', 'http://www.miracledentalnv.com', 'https://www.zyn.ca', 'http://airbagit.com', 'http://www.lkqpreschool.com', 'http://www.gigglesandgrinsdds.com', 'http://www.portofsubs.com', 'https://tntcigars.com', 'http://lewisfamilytattoocompany.ca', 'http://www.jarrettandraja.com', 'http://www.theverve360.com', 'https://uronsalon.com', None, 'http://www.southsidemarkham.com/index.htm', None, None, 'http://www.lv-permanentmakeup.com', 'http://barre3.com/studio-locations/paradise-valley', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'https://www.dennystransmission.com', 'https://stores.musicarts.com/gilbert?source=LGOA5LKA', 'http://www.superstitionmountainmusic.com', 'https://www.kindercare.com/our-centers/charlotte/nc/300435?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=300435', 'http://www.cobbsadventurepark.com', None, 'http://nutechautocentre.mechanicnet.com', None, None, 'https://www.thompsonhotels.com/hotels/canada/toronto/thompson-toronto/restaurants/lobby-bar?utm_source=yelp.com&utm_medium=media&utm_term=thompson-lobby-bar&utm_content=homepage&utm_campaign=business-listing', 'https://stores.hallmark.com/pa/pittsburgh/amys-hallmark-shop-pittsburgh-pa-27613.html', 'https://skylarksocialclub.com/coming-soon/', 'https://www.promises.com/locations/promises-scottsdale/', None, 'http://www.woehlerlandscaping.com/', 'http://charlottemobilesolutions.com', 'https://www.andersenbroyles.com', None, 'http://saxonjewelers.com', None, 'http://frillylilly.ca/boutiques/frilly-lilly-mission', '1592924968', None, '1592924975', 'https://www.dermaster-az.com', None, 'http://www.g-mart.com', 'http://www.azcasinoknights.com', 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpsouthwestorganic', 'http://www.donjuan-restaurant.com', None, None, None, 'http://www.drpalamone.com', None, 'https://www.4wheelparts.ca/stores/alberta/4wp-calgary-ab-1024', 'http://www.lavitasalonandspa.com', None, 'https://ad.doubleclick.net/ddm/clk/458685290;262921492;t', None, None, 'http://www.verizonwireless.com/stores/ohio/fairview-park/rocky-river-322485/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.shamrockbarandgrille.com', None, 'https://www.phoenix.gov/parks/recreation-and-community-centers/centers-b/beuf', 'http://www.pizzahut.ca/', None, 'http://www.meridianlandscape.com', None, 'http://www.kolorartistry.com', 'http://www.petplanethealth.com/stores/country-hills-town-centre/', 'http://www.rockwelrealty.com', 'http://bk.com/', 'https://www.infinitebeautymedspaaz.com', 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6733', 'https://barks-and-recreation.com', 'http://www.campbellandassociateslaw.com', None, 'http://www.macssushi.com', None, 'http://cornerstonepgh.com', 'http://freshpaintstudio.ca', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.nakedgrape.net/', None, None, 'http://thefirmpr.com/', 'https://www.taolasvegas.com/restaurant?utm_campaign=TAOAB&utm_medium=Inquiry&utm_source=Yelp', 'http://www.mychickenshack.com', 'https://www.toughturtleturf.com/artificial-grass-las-vegas-nv', 'https://kocianmeats.com', None, 'http://www.power9games.com', 'https://www.iautohaus.com', 'https://siemprealgopgh.com', None, 'https://www.williams-sonoma.com', 'http://www.grandparkdental.com', 'https://www.robson.com/communities/pebblecreek/', 'http://octopuspoolservice.com', 'http://www.integra-accounting.net', 'http://www.lornajane.com', 'http://chagrinfallspetclinic.com', 'http://rebootgaminglv.com', 'http://in-n-outpizzacafe.com', 'http://www.caseycaters.com', 'http://kcmautocare.com', 'https://barbershopinscottsdale.com', None, 'http://www.littlebearconstruction.org', 'http://www.adiamopalmvalleyapts.com/floorplans.aspx', '1592925212', 'http://www.vegaslashes21.com', 'http://www.caldensebakery.ca', None, '1592925223', '1592925228', 'http://www.lamadeleine.com', 'https://locations.wendys.com/united-states/az/gilbert/929-n.-arizona-avenue', 'https://sunsetstation.sclv.com/Gaming/Bingo/?utm_term=SS&utm_content=SS-PROPERTIES&utm_medium=SOCIAL&utm_source=YELP&utm_campaign=SS-YELP', None, None, 'https://www.t-mobile.com/store-locator/az/chandler/chandler-fashion-center?cmpid=WTR_SE_YXT_U98MLWB9027148', None, None, 'http://www.nedrebos.com', 'http://www.capraesuidae.com', 'http://www.fifty-1.com', 'https://www.241pizza.com', None, 'http://larrysvilla.us', None, 'https://www.moonvalleynurseries.com/locations/phoenix?utm_campaign=yelp&utm_source=yelp-az&utm_medium=phoenix', '1592925278', None, 'http://www.azfairtrade.com', None, 'https://www.wellsfargo.com', 'http://www.tuesdaymorning.com', None, 'http://www.drpaintllc.com', 'http://www.canadiantire.ca/en/store-details/on/sheppard-and-leslie-on.store.html', 'https://www.azvalleywindows.com', 'http://www.taxmanplus.com', '1592925314', 'http://deseretbook.com/stores/show/86', 'http://lafrontera-empact.org', None, 'http://www.tigerlily.com', 'http://www.dollar.com', 'http://clickserve.dartsearch.net/link/click?lid=43700040271614300&ds_s_kwgid=58700004686038588&ds_url_v=2', 'https://www1.shoppersdrugmart.ca', 'http://www.bahamabucks.com/', None, 'https://www.bowlero.com/location/bowlero-christown?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'http://discoverydentalnv.com', 'http://www.foxspizza.com/locations/oh/north-olmsted/north-olmsted-oh-315/index.html', None, '1592925357', 'http://www.anothermother.net', None, None, 'http://7salonandspa.com', 'https://www.adt.com/new-media/home-security?ecid=nafresi00079', 'http://www.thepersianpalace.ca', 'http://www.mineospizza.com/', None, 'http://www.sanctuarybyjoyce.com', 'https://www.longos.com/store/liberty-village', 'http://www.appliancepros.net', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.timhortons.com/', 'http://www.chapters.indigo.ca/en-ca/home/storelocator/storeDetails/927/', None, 'http://www.furnituremarkdowns.com', None, 'http://laurelrichards.com', 'http://www.ogdenvault.com', 'http://www.unicorncupcakeboutique.com', 'http://www.swingpt.com', None, 'https://www.kohls.com/stores/az/phoenix-1102.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.mysisterscharities.org', None, 'https://client.schwab.com/public/branchlocator/branchdetails.aspx?localdir=yelp&branchid=1304', 'http://www.pinnaclepeakpodiatry.com', 'http://www.pghsandwichsociety.com', 'http://locations.saksoff5th.com/en/glendale', None, 'http://www.lesfillettes.com/', None, 'http://thaimango.ca', 'http://www.canyonfallsvegas.com', 'http://www.merveillespa.com/', None, 'http://www.starbucks.com/store/14175/', 'http://www.idascookies.com', 'http://www.jackify.com', 'http://www.sociablepub.com/', 'http://www.parsisandwich.com', 'http://www.roundcornercantina.com', 'http://www.collinscollege.edu', 'http://www.pinnaclepeakinsurancegroup.com', None, '1592925502', None, 'http://www.phaselinedefense.com', 'http://www.christopherstalbergmd.com', 'http://radioshack.com', None, None, None, 'http://www.jambajuice.com', None, None, 'https://www.shopnyla.com', 'http://www.mokshayogacalgary.com', 'http://www.hilgerspedo.com', None, 'http://www.vividracing.com', 'http://www.fringesalonofmadison.com/', 'http://www.lumensalon.com', 'http://www.lavahairsalon.com', 'http://www.bebe.com', None, 'https://fitbodybootcamp.com/northphoenixfitnessbootcamp/', None, 'http://www.essentialsverona.com', None, 'http://www.cardenasmarkets.com/', 'https://twomenandatruck.ca/movers/on/etobicoke?utm_source=Yelp&utm_medium=organic', 'https://www.goodeyes.com/locations/green-valley/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-greenvalley&utm_content=website', 'http://www.banfield.com?utm_source=yelp&utm_medium=PAID&utm_content=yelp_general&utm_campaign=YelpPaid', None, 'http://www.pawn1st.com/locations/scottsdale-az', None, 'http://www.foothillsrehab.com/', None, 'http://www.eatatrubins.com/', None, 'https://tonyandnicksplace.com', 'http://www.duchessonline.com/', 'http://www.windsorarmshotel.com/cafe_desc/', 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', None, 'http://www.desertskygames.com', 'http://www.spayaz.com/locations/chandler-az/', 'http://www.adcoservice.com', 'http://www.oliveannie.com', 'https://www.nofrills.ca/store-locator/Listro%27s+nofrills+%28Markham+Rd.%29/0788?storeId=0788', 'http://yelp.com/elite', 'http://www.southbuffalospringsanimalhospital.com', '1592925656', '1592925660', None, 'http://www.calistogagrill.ca/', None, None, 'https://stores.guitarcenter.com/n-olmsted?source=4GOA5AJBB', None, 'http://vcanorthviewspecialty.com', 'http://www.zergott.com', 'https://pho-ok-vietnamese-restaurant.business.site', 'http://www.animalkingdomaz.com/', None, 'http://www.ltayh.com', 'http://www.planetfitness.com/gyms/belmont-park-st-nc-522?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.woobuffet.com', 'https://www.consumeropinionservices.com', 'https://sites.google.com/site/sjmexterminating', None, None, None, 'http://www.getbetterfaster.ca/', None, 'http://www.cakestar.ca', None, 'http://woodbineendoscopy.com', None, '1592925743', 'http://capellaplace.com', None, None, None, 'http://www.tov-li.com', 'http://www.clubxs.ca/', 'http://www.taycoelectric.com', 'http://www.theteapotus.com', 'http://www.wildburger.ca', 'http://www.flyright-aviation.com', 'https://www.upack.com', 'http://www.caniglia.com', 'http://www.homehardware.ca/en/dealer-microsites/1234-0/contact-information.htm', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://solarscreencity.com', 'http://www.cigarsforyou.ca', 'http://www.thebarberschair.ca', 'http://www.dancestarzaz.com/', 'http://www.kelseys.ca', 'http://www.carolinabluepoolsaz.com', 'http://www.kurtsironpoolfencing.com', 'https://www.novaspine.net', 'http://www.angeloslakewood.com', None, None, 'https://buckeyeaz.hbcarpetcleaning.com', 'http://www.littlecaesars.com/', None, None, 'http://www.paradisevalleyfootandankle.com', 'http://www.epicthriftstores.com/', None, 'http://www.tropicalsmoothie.com', None, 'http://www.kiehls.ca', 'http://www.foodlion.com', 'http://www.mufflers4lesscleveland.com/', 'http://www.BaldwinEyeCareLLC.com', 'http://theoriginalrainbowdonuts.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://affordablelockaz.com', None, None, 'http://www.dollarama.com', 'https://www.speedyglass.com/store/eagleriver/', 'http://www.ricetrax.com/', 'http://www.dunkindonuts.com', 'https://www.myprose.com/boutiques/phoenix/', 'http://www.sprint.com', None, None, 'http://www.royalinteriorcleaning.com/', 'http://www.bobmayberryhyundai.com', 'https://erin2026.wixsite.com/poundersbarandgrill', 'http://toronto.swea.org', 'http://www.arizonaartificiallawns.com', 'http://www.burntwoodtavern.com', 'http://www.spotfreecarwash.ca', 'http://dubinwellness.com', 'http://saskiasalon.com', 'http://www.desertviewdentalcare.com/', 'https://junipercocktail.com', 'http://www.mrappliance.com/west-las-vegas', 'http://www.jetclosing.com', None, 'http://www.childrensedationdentist.com', 'https://www.ticketbusters.com', 'http://www.centurypaintingnc.com', 'http://www.goodyearair.com', 'http://www.perrymongesalon.com/', 'https://www.jerryschwickrathwindowcleaning.com', 'https://dutchbros.com/?utm_source=phoenix&utm_medium=yelp&utm_campaign=website_phoenix', None, 'https://www.thewalkingcompany.com/shoe_store/349/az/gilbert/san_tan%20village', 'http://suncityvacuumsandsewing.com', None, 'http://www.wonderpixelphotography.com', 'http://www.donscaribbeanjerk.com', 'http://www.thepalmsonscottsdale.com', None, 'http://www.completedentallv.com', 'http://www.closetsbydesign.com', 'http://www.finishline.com', 'http://www.procutproplow.com', None, 'http://www.champaignchryslerdodgejeep.com', None, 'http://www.sekushi-vegas.com', 'https://www.tropicaltreasuresphoenix.com', 'http://www.clearinghousesouth.com', None, 'http://www.travelshots.net', 'http://www.JimmyJohns.com', 'http://nvtac.com', 'http://www.cbs5az.com', 'http://freshii.com', '1592926074', 'https://www.zaxbys.com/locations/nc/indian-trail/13967-independence-e-blvd/', 'http://www.charmeck.org', None, None, None, None, 'http://www.integritychiropractic.com', None, 'https://www.hilton.com/en/hotels/phxcrhx-hampton-suites-phoenix-chandler-fashion-center-az/?SEO_id=YELP-HP-PHXCRHX', 'http://jptowing.com/', 'http://www.cvnailspa2.com', 'https://www.officedepot.com/storelocator/nv/las-vegas/office-depot-3351/', 'http://kapusokapamilyalasvegas2.restaurant-facilities.com', 'http://www.burntwoodtavern.com', 'http://www.lasvegasticketauthority.com', 'http://www.steakandstone.com', None, None, None, 'https://find.shell.com/us/fuel/10010465-7201-e-cave-creek-rd/en_US', 'http://frillylilly.ca/boutiques/frilly-lilly-mission', 'http://www.sweetolenkas.ca/', 'http://www.makepapereasy.com', '1592926153', 'http://www.zumiez.com', '1592926159', 'http://www.bonzcharlotte.com', None, None, None, None, None, None, 'http://locations.saksoff5th.com/en/bramalea', None, 'http://spiritofyork.com', 'http://www.angelospizzavegas.com', 'https://locations.vitaminshoppe.com/az/phoenix/vitamins-supplements-phoenix-az-210.html', 'http://www.internationalmotorcars.ca', 'https://www.choicehotels.com/ohio/mayfield-heights/comfort-inn-hotels/oh502/rates', 'http://newserenityspa.com', 'http://www.silverstatecu.com', 'https://nationwidevision.com/locations', 'http://www.platosclosetcharlotte.com/', '1592926224', 'http://www.tuffyeuclid.com', 'http://www.alliedsurplus.com/', None, 'http://www.evct.org', 'http://computermekanix1.com', 'http://www.guansautoservice.ca', None, None, 'http://www.clubhillbrook.com', None, 'http://www.dunkindonuts.com', 'http://www.oasislasvegasrvresort.com', 'http://www.weecare4kids.com', 'http://www.sammich.co', 'http://www.montessoriacademyaz.org', 'http://www.allergyasthmaclinic.net', None, None, 'http://www.cariboucoffee.com', 'https://www.circlek.com/store-locator/us/youngtown/13216-n-111th-ave/2700054', 'https://www.kesslerandsons.com', 'https://www.brakemasters.com/new-site/stores/1901-n-scottsdale-rd-scottsdale-az/', 'http://www.vikingbakery.ca', 'http://motomaxcycles.com', None, 'http://www.psiconstructionllc.com', None, 'http://newyorkflavor.com', None, None, None, 'http://TrueGoddessHair.com', 'http://www.drbudny.com', None, None, 'http://www.dx.org', 'http://www.drlee-knight.com', 'http://www.cycfitness.com', 'http://www.wipliance.com', None, '1592926351', 'https://wildfire.sclv.com/Wildfires/Wildfire-Sunset?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', '1592926359', 'http://www.bouldercitystore.com', 'http://darumacalgary.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.drainproplumbing.com', 'http://blitzfacialbar.com/location-leslieville/', 'http://www.seranopizzeria.com', 'http://www.morfurniture.com', None, 'http://phoenixmercantile.com', '1592926397', 'http://www.shoeteria.com', 'http://www.comparesupermarkets.com', 'http://www.boldtair.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.timhortons.com', 'http://www.buffaloexchange.com/location-details/lasvegas', 'http://www.lapeaudermatology.com', None, 'https://bricksandminifigs.com/store/phoenix-arizona', None, 'http://www.flamekabobvegas.com', 'http://www.sunvalleysolar.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEAP', 'http://www.curesstudio.com', 'http://knightperformance.net', 'http://bk.com/', 'https://www.amctheatres.com/movie-theatres/charlotte/amc-concord-mills-24?utm_uid=yelp', 'http://redeyegrafix.com', 'http://www.starbucks.com/store/9334/', None, 'http://www.flatratewindowcleaning.com', 'http://www.samstownlv.com/dine/the-angry-butcher?disid=wmm_yelp_st_corporate_angrybutcher_organiclink', 'http://beadsandplentymore.ca', 'http://browart23.com', 'http://elnopalmexicangrill.com', 'https://khazanaindianbistro.business.site', 'http://w.subway.com', None, None, 'http://www.papajohns.com', 'http://sunnyhillspainclinic.com', 'http://www.lickshomeburgers.com', 'http://www.bigelowlimo.com', None, 'http://www.hottopic.com', 'https://www.circlek.com/store-locator/us/tempe/802-s-hardy-dr/2700039', 'http://www.allseasonmotorsports.ca/', 'http://www.mygnp.com/store', '1592926540', 'http://www.whiskeyranchbbq.com/', None, None, None, 'http://www.donsappliances.com', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'https://homesmart.com/real-estate-agent/arizona/scottsdale/51949-richard-howell/Welcome', 'http://www.desertspringsapts.com', 'http://www.excaliburcollisioninc.com', None, None, None, 'https://www.thaihealingsolutions.com', 'http://www.tntcigar.com/', 'http://grillway.ca/', 'http://www.papajohns.com', 'http://thaidelight.ca', None, None, 'http://www.purefitlv.com', None, 'http://worksburger.com', None, None, 'http://www.comedybar.ca', 'http://www.divasalonspa.com/', 'http://www.tempepaintball.com', 'http://www.sizzlekoreanbbq.com', 'http://www.goodlifefitness.com', 'http://www.cleanjuice.com', None, 'http://europeanfoodcharlotte.com', None, None, 'http://www.auntieannes.com', 'http://www.gcwomenscenter.org', 'http://www.planetfitness.com/gyms/north-huntingdon-pa-911?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'https://ad.doubleclick.net/ddm/clk/434343698;236814625;q', 'http://homecallchiropractic.com', None, 'http://www.twinmaidservice.com/#!home/mainPage', 'http://www.meatonthebeach.com', 'http://www.federalgalley.org', '1592926690', 'https://www.hilton.com/en/hotels/pithahx-hampton-suites-pittsburgh-harmarville/?SEO_id=YELP-HP-PITHAHX', 'http://30minutealterations.com/', 'http://doomiestoronto.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://shine-wellness.com', None, 'http://www.cioppinopittsburgh.com', None, None, None, 'http://www.forteessalon.com', 'https://www.rightnowair.com', 'http://aandaauto.com', 'http://www.azhear.com', 'https://www.airportmazda.ca', 'http://www.ruggerolidds.com', '1592926751', 'http://www.totaldentallkn.com', 'http://www.ilovemichaels.com/', 'http://www.cleatswings.com', 'http://www.gentsboxingclub.com', 'http://www.riorestaurant.ca', None, 'http://www.tuesdaymorning.com/index.jsp', None, 'http://www.housecleaningmadison.com', 'http://www.friendselectricians.com', 'http://whasn.com/main/doctors/6', 'http://www.starbucks.com/store/9595/', 'http://www.outsideinnvegas.com', None, 'http://www.lv12volt.com', 'https://www.morgan-properties.com/apartments/pa/pittsburgh/governors-ridge/', 'http://www.phoenixinternet.com', None, 'http://www.illinioilchange.com', 'http://desertvalleygastro.com/', 'http://kimnailpittsburgh.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.hartwitzengallery.com/', '1592928981', 'http://www.53.com', 'https://www.supercuts.com/locations/pa/pittsburgh/shadyside-plaza-s-highland-haircuts-8953.html', 'http://www.superstarcarwashaz.com/fullservice.php', None, 'http://www.lalousalon.com/', '1592928997', 'http://energyptaz.com', 'http://www.the-alley.ca', 'http://www.cabaretvintage.com', None, 'http://unbouncepages.com/mynvdmv', None, 'http://www.barcelonariversedge.com', 'http://www.ccvstars.com', 'http://www.desertvalleypediatricslv.com', 'http://www.kmansell.com', None, None, 'http://www.sussex1939.com/', None, None, 'https://www.blinebikepark.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTUL', None, 'https://apsnevada.com', None, 'http://www.tfpest.com', None, 'http://www.monroestreetfarmersmarket.org/index.html', None, 'http://www.tacolandiaphx.com', 'https://www.stayalfred.com/property/stay-alfred-at-broadstone-scottsdale-quarter/?utm_source=Yelp&utm_medium=Scottsdale&utm_campaign=Broadstone_Scottsdale_Quarter', 'http://www.cornercafeandcatering.net', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'http://www.firstclassgreencleaning.com', None, 'http://111-dundas-st-w-toronto.bareburger.com', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', None, 'http://www.golfblackmountain.com', 'http://www.daintilypolished.com', 'http://www.lcbo.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/14600+Lawyers+Road+Corner+Of+Stevens+Mill+Road-Matthews-NC-28104/storeid=2877?cid=ps_ylp_2020', None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-osborn?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-osborn', 'http://www.marks.com', 'http://www.goldfingersnails.com', 'http://www.dilworthdrug.com', None, 'http://www.arena51lasertag.com', 'http://table9cleveland.com/', 'http://www.huntlv.com', None, 'https://www.choicehotels.com/arizona/mesa/sleep-inn-hotels/az022/rates', 'http://www.legacy521.com', '1592929159', None, None, 'http://www.mrhero.com', 'http://www.theharpaz.com/', 'http://www.drivingarizona.net/', 'https://www.dinnerwithaview.ca', 'https://www.windsorstore.com/blogs/store-locator/nv-las-vegas-downtown-summerlin-mall', 'http://www.fabricland.ca/MAIN/main.php', 'http://www.sedonalv.com', 'https://local.safeway.com/safeway/az/phoenix/3132-e-camelback-rd.html', None, None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=10538&localechange=1', 'http://www.birchmountcollision.com', None, 'http://www.hermosastudios.com/', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZMR', '1592929220', 'http://phoenixnorthwest.directbuy.com/?utm_campaign=Yelp+Organic&utm_medium=Local+Listings&utm_source=Yelp', None, 'https://www.oneazcu.com/about/locations/gilbert-guadalupe-rd/', '1592929234', None, 'http://info.lululemon.com/stores/us/las-vegas/fashionshowmall', 'http://www.petco.com', 'http://www.duzaskitchen.com', 'http://www.breadheadslv.com', 'http://www.apple.com/ca/retail/marketmall/', 'http://www.bbappliances.com', 'http://troxtech.co', None, 'http://www.ironaddicts-lasvegas.com', None, None, 'http://www.lvhomesgroup.com', None, 'http://www.brittshairchair.com', 'http://www.bipargriebdentistry.com', None, 'https://www.fastmed.com/urgent-care-centers/surprise-az-walk-in-clinic/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.citysurffitness.com/tempe#tempe-location', 'http://powerblackbelt.com', None, 'http://portofinogaston.com', 'http://www.2sonsplumbingaz.com', 'https://www.thingzcontemporary.com', None, 'http://www.brandongynecology.com/', 'http://www.torontohealthcentre.ca/', 'http://www.antiquerosefloristllc.com', None, None, None, 'http://www.treelinedesigngroup.com', 'http://www.bernarddogrun.org/about/', 'http://www.ciccantis.com', 'http://www.mymothershouselv.com', 'http://atelierwellington.com', None, None, 'http://www.vdara.com/amenities/vdara-pool-lounge.aspx', None, 'https://kactuskushcbd.com', None, None, None, 'http://www.integrativehealthinstitute.ca', 'https://authenticcustomcabinetry.com', None, 'http://www.poffspineandjoint.com/', 'https://www.publicstorage.com/arizona/self-storage-surprise-az/85379-self-storage/2289?pid=wyelp&CID=1245&CHID=AFL', None, 'http://mrsub.ca', None, 'http://www.wendys.com/', None, None, 'http://www.canadacomputers.com/location.php#13', 'http://alignyourhealth.com', 'https://www.tempecitytacos.com', 'https://www.catsnap.org', 'http://www.imsaz.com', 'http://www.cloud9homeservices.com', 'https://locations.theupsstore.com/oh/rocky-river/19885-detroit-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.strengthtrainingrehab.com', 'http://www.coolbeansmedina.com/', None, 'http://www.shescraftyboutique.com', 'http://www.pizzahotwings.com', 'http://www.ableplumbingsolutions.com', 'http://www.timbersgaming.com', None, None, 'http://www.royalcarriagelv.com', 'https://child-care-preschool.brighthorizons.com/NV/LasVegas/mgm', 'http://cleanablind.ca/', None, 'http://www.puttersvegas.com/', '1592929472', 'http://www.sherwin-williams.com/store-locator/paint-store/Henderson/KY/1193', 'http://www.montevistacleaners.com', None, None, None, 'http://www.procyclery.com', 'https://www.crateandbarrel.com/Stores/legacy-village/str753', 'https://uberwash.business.site', 'http://www.victorylanekarting.com', 'http://8950cbp.com', 'https://coplons.wordpress.com', None, 'http://www.bodyawakeningsaz.com', 'http://www.clothandflame.com', 'http://www.skyzone.com/madison', 'https://www.walmart.com/store/5334/aurora-co/details', None, '1592929513', 'http://www.bulgergallery.com', 'http://www.cravindonuts.com/', None, 'http://www.wagnerhomesvc.com', None, 'http://www.clsphx.org', None, 'http://www.timhortons.com/', None, 'http://www.hottiesworld.com', None, 'http://www.gtaexotics.ca', 'http://www.express.com', 'http://www.wendys.com/', 'http://www.madisongreenbox.com', 'http://octopusgardenyoga.com', 'https://www.publicstorage.com/north-carolina/self-storage-monroe-nc/28110-self-storage/2100?pid=wyelp&CID=1245&CHID=AFL', 'https://www.canyonofs.com/oral-surgery-las-vegas-nv-centennial-hills', None, 'http://www.americaneyeglassrepair.com', 'http://www.teriyakiexperience.com', None, 'http://www.tatumranchvet.com/', 'http://www.madisonhairdesigners.com', None, 'https://www.scottsdaleplaza.com', 'http://www.centralmusicdirect.com', 'https://escaperoomclev.com/escape-room-strongsville/', 'http://mooneymovers.com/', None, 'https://mymhcommunity.com/Communities/Arizona/SeyennaVistas/?utm_campaign=Yelp_Directory_Listing&utm_medium=directory&utm_source=Yelp', 'http://www.whiskeyjacksmadtown.com', 'https://www.homedepot.com/l/North-Mesa/AZ/Mesa/85204/473?cm_mmc=seo-yelp&', 'http://reliancefloor.com', None, 'http://www.rotistop.com', 'http://www.midas.com/cleveland/store.aspx?shopnum=6454&dmanum=212', 'http://www.dunkindonuts.com', 'https://cacao70.com/en/our-locations/springborough', None, 'http://www.fatbottomcrossfit.com', None, 'https://www.aiyproperties.com/apartments/oh/akron/woods-of-fairlawn', '1592929625', 'http://www.copy-king.com', 'https://www.jrperkins.com', None, 'https://chatters.ca', 'https://nyscollection.com', None, 'https://www.interdent.com/gentle-dental/locations/az/gilbert/81-w-guadalupe-rd-dentist-office?utm_source=organic&utm_medium=yext', 'http://pizzaranch.com/', None, None, 'http://elitegranderestaurant.com', 'https://www.alarmsbykrystal.com', 'http://camelbackpetdoors.com/', 'http://coconuthutaz.com/', 'https://www.nolashairsalon.com', 'http://nicolekingpalabra.salonrunner.com', None, 'http://vipvegasclubcrawl.com', 'http://www.lightfactory.org', None, 'http://www.jaredblakeentertainment.com', 'http://bareescentuals.com/on/demandware.store/Sites-BareEscentuals-Site/default/Home-Show?brandId=BM&cm_mmc=Yelp_-_Campaign_1', 'http://www.honeybearsbbq.com', 'http://www.redrobin.com/', None, 'http://www.parkridgevacuum.com', None, 'http://www.motherhood.com', None, 'http://www.oceans7az.com', 'http://www.riversidepethospital.ca', 'http://superfuzzaudio.com/', None, 'http://www.thebay.com', 'http://www.valleyofthesunderm.com', 'http://www.mingleslounge.com', 'http://sumitsnorthphoenix.com', 'http://www.ofixit.com', 'http://www.oldnavy.com', 'http://www.clevclassictattoo.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.joshuahongdds.com', 'http://www.trilogyphysio.com', None, '1592929735', 'http://libanst.ca', None, None, 'http://www.furniture7.com', 'http://spurssaloonaz.com/', 'https://www.healthysmilesphoenix.com', None, 'http://www.charlottepediatricclinic.com', None, 'https://www1.shoppersdrugmart.ca', 'http://www.indiancrown.com', 'http://www.betteridgejewelers.com', 'http://www.pusadeesgarden.com', 'http://meineke.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.swishvegas.com', 'http://www.allcitytowing.com', 'https://locations.wafflehouse.com/sc-rock-hill-1120', 'http://www.bk.com', 'http://www.baskinrobbins.ca', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', None, 'https://stores.partycity.com/ca/ab/calgary/party-store-ca2145.html', 'http://www.franksonsheacondos.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.thaihealingartscenter.com', 'http://www.avinspect.com', 'https://www.blueherondentistry.com', 'http://poolchemaz.com', None, None, 'http://fluidevents.org', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.softmoc.com', None, 'http://vimispa.ca/', 'http://www.montysmusic.net/index.html', 'https://www.walgreens.com/locator/walgreens-1654+n+pebble+creek+pkwy-goodyear-az-85395/id=12334', 'http://www.farmfreshcarolinas.com', 'https://www.staples.com', 'http://j-alibaba.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282947950&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.thepreferredrealty.com', 'http://www.lexmarusa.com/', 'http://www.arbys.com', 'http://www.grandmahelenskitchen.com', 'http://www.livingwordonline.com', 'https://www.exitstrategyus.com', None, 'http://sunstoppers.com', None, None, 'http://tasteofpunjabltd.ca', 'http://www.todaysdentalvegas.com', 'https://www.walmart.com/store/2592/north-las-vegas-nv/whats-new', 'http://www.madareadriving.com', 'http://www.thehealthybutcher.com', 'https://sojkabobexpress.business.site', None, None, 'http://www.therootcanalguy.com', None, 'https://oralsurgerymadison.com', None, 'http://www.tomosushi.ca', 'http://chicagobrewinglv.com', 'http://lasvegas.carenow.com/location/cheyenne-durango', None, None, None, 'http://www.budgetlockaz.com', 'http://www.lasvegashomesdirectory.com', '1592929961', 'http://www.ballantineflowers.com', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_434', None, None, 'http://www.maloneystavern.com', None, 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://www.joesdineraz.com/', 'http://azcoolphx.com', 'http://www.modernclassicsclt.com', None, 'http://hotyam.ca/', 'http://richmondhillartschool.com/', None, None, None, None, 'http://www.walmart.ca/en/toronto/3106', None, 'http://www.mindbodyandflow.com', None, 'http://www.applianceservice-center.com', 'http://superiorclean99.com', None, None, 'http://www.actux.com', 'http://www.homespecaz.com', 'http://azpaindoctors.com', None, 'http://www.702dtlv.com', None, 'http://www.owensbagelanddeli.com', None, 'http://phoenix.gov/DOWNTOWN/patriots.html', None, None, None, 'http://shortandsweetcupcakes.ca', 'http://www.moderndaychimney.com/', None, 'http://www.5thandwine.com', None, None, 'http://iconicautoexchange.com', 'http://www.phxskin.com', 'http://fiveguys.com', None, 'http://www.7-eleven.com/?yelp=29663', 'http://clownytattooshop.com', None, 'https://www.aryanacuisineyyc.ca', 'https://www.southsideplumbingandheating.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.gdallashorton.com', 'http://www.luxur-e.com', 'http://www.silverminesubs.com/', 'http://magicshoerepairlv.com', 'https://www.agelesskarate.com', 'http://www.randstad.ca', 'http://www.top10tattoobarbershop.com', None, None, None, 'http://www.mayoclinic.org/familymedicine-sct/thunderbird.html', 'http://locations.michaels.com/pa/bethel-park/9944/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.thunderbird.edu', 'http://www.yourwaxingstudio.com', 'http://www.ryanjanet.com?cmpid=PRGN_BLM_0006', 'http://modernlovers.ca/', 'http://www.twistedcurry.com', '1592930202', None, 'http://www.thewoodenspoonconcord.com', 'http://www.VegasHomeAgent.com', 'http://www.fox5vegas.com/', 'http://www.theclaytononthepark.com', '1592930224', 'http://music-calgary.com', 'http://lennardsplumbinginc1.godaddysites.com', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/matthews/staie/hoteldetail', 'https://www.housing.wisc.edu/dining-locations-gordon.htm', 'http://www.abuelos.com', None, None, 'http://kathyspastryshop.com/', 'http://www.winners.ca', 'http://www.epocagroup.com', None, None, 'http://chuckspainting.net', '1592930276', 'https://locations.theupsstore.com/oh/akron/3465-s-arlington-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.mattressfirm.com', 'http://www.WeTreatSoreFeet.com', 'http://www.beerminimum.com', None, 'http://www.fortmillplayhouse.org/', 'https://www.familydollar.com/locations/az/phoenix/26308', 'http://www.sixthstreetdental.com', None, '1592930312', None, 'http://www.thefishersrealestate.com', 'https://www.ashleyfurniturehomestore.com', 'http://www.boulevardbarandgrille.com/', None, 'https://www.perfecthairandmakeup.com', 'http://jjsfreshkitchenbar.com', 'https://www.tgifridays.com/locations/1852/fridays-las-vegas-west-nevada', 'http://www.lamexicana.ca/', None, 'http://www.wendys.com/', None, None, None, 'http://www.captaintonys.com/captain-tonys-pizza-cleveland-ohio-9th-street/', 'http://www.franksbratwurst.com/', 'http://www.ihg.com/staybridge/hotels/us/en/chandler/phxot/hoteldetail', 'http://www.southmountainpoolservice.com', None, 'https://mesa.wini.com', 'http://www.tequilasgastonia.com', None, 'http://www.phxicerink.com', 'http://www.aphroditecooks.com/', 'http://tradesmantavernparma.cf', 'http://www.kibosushi.com', None, 'https://www.charmingcharlie.com/stores/details?fbclid=IwAR2iVQG7_fMOeTbff-jnFBIBUoJ6zTqolugguTMj5OSr19367S2YCqjPoZo&stid=107', 'http://ensoteabar.com', 'http://www.winghouseandsportsbar.com/', 'http://www.akronymca.org', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://kcanimalhospital.com', 'https://stores.bestbuy.com/az/scottsdale/15449-n-hayden-rd-870.html/?loc=ns100&ref=NS', 'https://www.canyonstatecu.org', 'http://bathurstglengolf.ca/', 'http://www.hundrednorthbar.com', '1592930444', None, 'http://www.mdautodoctors.com', None, 'http://desotoexterminating.com', 'http://www.neveriachayos.com', 'http://www.perkopolis.com', None, 'http://www.preterm.org', None, 'http://www.insightglobal.com', 'http://spineanddisc.net', None, None, 'http://www.kaijugames.ca', 'http://www.goldiesmotors.com', None, None, None, 'http://jerrysrestaurants.com', 'http://www.picobarbershops.com', 'http://www.cravegrillhouse.com/', 'https://www.sanctuaryoncamelback.com/dining/elements/', 'http://www.myblockfence.com', 'http://www.scottsdalevascularservices.com', 'https://www.dairygrove.com', 'http://www.comoncy.com/', 'http://ilfornello.com/bayview/', None, 'https://www.loresouthmountain-apts.com', 'http://www.earthsmartdesign.com', 'http://www.kaitoldyouso.com', 'http://saralasvegas.com', 'http://www.eoclinic.com', 'http://www.tikitaxi.ca', 'https://www.trusighteyes.com', None, 'http://VillageSnow.com', None, 'https://www.cmlibrary.org/branch/main-library', 'https://microbytes.com/ptc.html', 'http://www.mathpro.ca', 'https://ad.doubleclick.net/ddm/clk/459140493;262878870;w', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/27713+Lorain+Road+Corner+Of+Porter+Road-North+Olmsted-OH-44070/storeid=2587?cid=ps_ylp_2020', None, 'https://towncentervet.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281381774&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://thehermitslamp.com', 'http://www.tlccleaners.ca', None, 'http://broadstonefashioncenter.com', 'http://www.gmpperformance.com/', 'https://eastmesaredmountain.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.reptilia.org/', 'https://www.searshomeservices.com/locations/appliance-repair/az-mesa/1425-w-southern-ave', 'http://casaverderestaurant.ca/', 'http://www.toyotaonfront.com', 'http://www.boardwalkplace.ca', None, 'https://www.walgreens.com/locator/walgreens-4+old+clairton+rd-pleasant+hills-pa-15236/id=9188', 'http://www.advanceicare.com', 'http://www.azoral.com', None, 'http://www.pussycatgelato.com', 'http://www.fitzone-plus.com', None, None, 'http://www.advantagecarrentals.com/locations/car-rental-east-york', 'https://locations.visionworks.com/ll/US/AZ/Goodyear/14009-W-McDowell-Rd', None, 'http://www.hazenightclub.com', 'http://www.nextcare.com/locations/az/tempe/?utm_source=Yelp&utm_medium=Local&utm_campaign=tempe', 'http://www.aturoguerra.wix.com/la-catrina-web-1', 'http://clickserve.dartsearch.net/link/click?lid=43700006435127049&ds_s_kwgid=58700000444950373&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.infinitiofbeachwood.com', 'http://caraudiolv.com', 'http://www.brighamandmore.com', 'http://www.giannachristine.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.williamoslerhc.on.ca', None, 'http://lasvegaswebdevelopmentinc.com/', 'http://www.nomorevertigo.com', 'http://www.selentis.com', None, 'https://eatmrmesquite.com', 'http://us.shop.ecco.com', None, 'http://www.realmomos.com', 'http://nailandbeautystation.business.site', None, 'https://simplyelegantcorp.com', 'http://libertynailstempe.com/', 'http://www.merrymaids-centralphoenix.com', 'http://www.tntbjj.com', 'http://www.graniteexpolv.com', 'https://lasvegas.kaisergarage.com/contact/location/', 'http://www.rossstores.com', 'http://thecarefulmove.net', 'http://Desertcanyonroofingllc.com', None, 'http://www.lvgolf.com/index.html/', 'http://www.stonebrookdrivingrange.com', None, 'http://www.lionhabitatranch.org', 'https://elevationchurch.org/locations/university-city/', 'https://www.popeyescanada.com/maps/richmondhill.php', 'http://www.royalhouse88.ca', None, 'http://www.thecorkfactory.com/the-cork-factory-pittsburgh-pa/', 'https://locations.wendys.com/united-states/wi/fitchburg/2858-fish-hatchery-road', 'http://urbanmaharajas.ca', 'http://www.supremeclubtours.com', 'http://advising.athabascau.ca/learning_centres.php', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=0895', None, 'http://www.hardees.com', 'http://www.rhythmkitchenlv.com/grandballroom.html', None, 'http://3ddreamsultrasound.com', None, None, 'http://alphillipslv.com/', 'http://www.eltororestaurante.com/', '1592930873', 'http://www.torontobodyworks.com/', None, None, 'http://www.tcsbbqcrib.com', None, None, 'https://www.lingerslumberjacks.com', 'https://www.dwwtc.com', '1592930899', 'http://www.schoolhousescoops.com', None, None, 'http://www.jimlebarbier.ca', 'http://www.sundvicklegacycenter.com', 'http://www.phoenixscottsdalegolf.com', 'http://www.pvschools.net/site/Default.aspx?PageID=87', None, 'http://www.humankanvas.com', 'http://stores.partycity.ca/on/markham/party-store-ca2010.html', 'http://acupunctureinvegas.com', 'https://www.myfitfoods.com/', None, None, None, 'http://www.localsonlytoronto.com', 'https://www.wyndhamhotels.com/hotel/46398?tel=18008899735&iata=00093785&cid=fe:hj:20170523:yl:pp:hjus:46398', 'https://grayhawk.viliving.com', None, 'http://www.hughsroomlive.com', None, 'http://www.gadgetexpertslasvegas.com/', None, 'http://thearrowcafe.com/', 'http://www.realfruitbubbletea.com', '1592930986', None, 'http://www.baldreemd.com/', 'http://www.behotyogatoronto.com/', 'http://www.arbys.com', 'https://www.supercuts.com/locations/az/glendale/bell-park-shopping-center-haircuts-80215.html', 'https://u-stor.com/locations/arizona/greenway/', 'http://www.letseat.at/PhiladelphiaDeliRestaurant', 'https://www.lalassalonspa.com', None, 'http://steveskrazysub.com', 'http://www.meadshardware.com', 'http://www.zimbrickhyundaieastside.com', None, None, 'http://charleys.com/', None, 'http://www.vicinopgh.com/', 'https://locations.churchs.com/nc-charlotte-598', 'https://www.bmoharris.com', 'http://www.corneaaz.com/index.php', '1592931060', 'https://www.jetblue.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://www.breathehotyoga.ca/', 'http://www.baskinrobbins.com', 'http://www.keepitsimplyclean.com/', 'http://stores.joann.com/az/peoria/1913/', None, 'http://www.4myvacation.com', 'http://www.denimandsmith.com', 'http://www.freddysusa.com/', None, 'http://www.bk.com', 'http://www.printsource1.com', 'http://www.redcanyonsupplyaz.com/', None, 'http://www.utilitysmart.com', 'https://bountygrill.ca', None, 'http://www.amberarlint.com/?cmpid=wj0l_blm_0006', None, None, 'http://www.JimmyJohns.com', None, 'http://www.sisterscentedcandles.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.menchies.com/frozen-yogurt-shops/frozen-yogurt-oakville-on', None, 'http://www.shawarmahut1.com', 'http://www.thecrystalcornerbar.com', 'http://www.portofsubs.com', 'http://www.janeadler.com', 'http://www.golfsmith.com', None, None, 'https://locations.theupsstore.com/nc/matthews/2217-matthews-township-pkwy?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://plumbingrepairphoenix.net', None, None, 'http://www.poolchlornv.com', 'http://www.rentlaprivada.com?campaign_code=yelp_La_Privada_AZ_85258', None, 'http://Hatfieldmedicalgroup.com', 'http://www.vipcollisionlv.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.imaginesalon-spa.com', 'http://www.tfwestrella.com', 'http://embroideryfromtheheart.com', 'http://www.azextremefit.com', 'http://www.agelessremediessouthpark.com', None, 'http://www.gelatospot.com/', 'http://www.coreybeck.com/', None, 'http://www.primrosepalmvalley.com/?utm_source=yelp&utm_medium=maplistings&utm_campaign=localmaps', 'http://www.chadenehring.com?cmpid=reaw_blm_0006', 'http://www.coachlissette.com', 'http://robertostacoshop.com', 'http://www.lulustacoshopaz.com', 'http://www.csn.edu', 'http://www.stareyebrowthreading.com/', None, 'http://www.adamikelectric.com', None, 'https://www.windsorstore.com/blogs/store-locator/wi-madison-madison-west-towne-mall', 'http://www.myfitnesselements.com', 'http://farmtotablepa.com/', 'http://www.freeportforwarding.com/', 'http://www.aznewbath.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://local.firestonecompleteautocare.com/arizona/scottsdale/13802-n-scottsdale-rd', 'https://www.royallepagesolutions.com/offices.php?oid=5', None, 'http://www.patcatans.com', 'http://stores.halloweencity.com/az/tempe/costume-store-4936.html', 'http://www.monsterchefcorp.com', 'http://frontstreetvet.com', None, None, 'https://store.vioc.com/nc/charlotte/4511-randolph-rd-28211-BD2901', 'http://www.allinwebpro.com', 'http://www.weddingtonwellness.com', 'http://www.eaglegunsandrange.net', 'http://roofproplus.com', 'http://www.cal-am.com/resorts/mesa-regal', 'http://mastodonpiercing.com', 'http://www.northernartists.com', 'http://www.sicilispizzalv.com/', None, 'http://www.tabaqrestaurants.com', 'http://www.602TheKing.com', 'http://locations.michaels.com/AB/CALGARY/3902/', None, 'https://www.mrahonline.com', '1592931388', 'http://www.calgary.ca/CSPS/Parks/Pages/Locations/NE-parks/Tom-Campbells-Hill.aspx', 'http://www.maidday.ca', 'http://www.paintdepot.com/location-oconnor.php', None, 'https://www.shoedeptencore.com', 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'http://www.bk.com', None, None, 'http://bellamoldremoval.com', 'https://www.gianteagle.com/Stores/Store/?storeId=440', 'http://carpetstarcarpetcleaning.net', 'http://www.keepitcleanlasvegas.com', None, 'http://www.53.com', 'http://www.clemetparks.com/recreation/tobogganing/', None, None, 'http://www.elitegaragedoor.com', None, 'https://holytrinity.to', 'https://www.redstarvapor.com/stores/vape-shop-glendale-olive-ave/', 'https://arfurnitureonline.com', None, 'http://mathnasium.com/glendale', 'http://www.swirltoronto.com/', 'http://www.purehotyoga.ca/', 'http://www.absolutappliancerepair.com/', 'https://www.gostorageone.com/self-storage/nv/las-vegas/durango-us-95', 'http://www.owlcleaners.com', '1592931485', 'https://locations.churchs.com/nv-north-las-vegas-331', None, None, 'http://lknpediatricdentistry.com', 'http://www.kelleysautorepair.com', 'http://www.lcbo.com', 'https://www.circlek.com/store-locator/us/gilbert/888-s-higley-rd/2703373', 'http://www.guitargallery.tv', 'http://www.boconcept.com/en-ca/stores/find-your-local-store/canada/boconcept-toronto', 'https://www.walmart.com/store/2281/west-mifflin-pa/whats-new', 'http://www.bootyswings.com', 'http://www.criminallawaz.com', 'http://www.bayviewvillagedental.com', None, 'http://www.southcharlottenissan.com', '1592931532', 'http://www.palmettogrillandbakery.com', None, None, 'https://www.ceenta.com/locations/university', None, None, 'http://www.vegassliders.com/', 'http://www.honesthandymanservice.com', 'http://www.lfoptical.com', 'http://www.mrsub.ca', 'http://www.HairByJacki.com/', '1592931575', 'https://www.gattomatto.ca', 'http://barsybanne.com', 'http://www.maptown.com', None, None, 'http://talaveratempe.com', 'http://north-carolina.flywheelsports.com/locations/ballantyne', 'http://freshfarmjuices.com', 'http://www.ceilingsetc.com', 'https://cobblestone.com/?utm_source=yelp%C3%8A', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.alohaohio.com', None, 'https://www.walmart.com/store/1380/las-vegas-nm/details', 'http://www.ocotillofamilydentistry.com/', 'http://www.sageandstem.com', 'http://www.donvalentino.ca/', 'http://ad.doubleclick.net/clk;266348169;92246478;a?http://mirage.com/nightlife/the-sports-bar.aspx', 'http://www.canyonpalmsapartments.net', 'http://rentanapt.com/lascolinas', 'http://www.kentfreelibrary.org/', None, 'http://www.sockmarket.com', 'https://www.lasvegasauction.com', None, 'https://www.drinkjozo.com', 'http://wienerschnitzel.com/', 'http://www.paulsacehardware.com', 'http://www.5starlimousine.ca', 'http://www.arazorsedge.com', None, 'http://www.daylightgrill.com', 'http://fixedratelocksmithnv.us', 'http://www.lvgroomer.com/warm-springs-grooming/', 'https://www.lasvegasbronzed.com', 'http://www.thelodgeslv.com', 'http://www.blastfitness.com/camelback', 'http://www.champaign.org', None, 'http://www.oliviasbanquet.com/', 'http://olivetschool.ca/', 'https://aquamermaid.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.designerkidswear.ca', 'http://shauns-towing.business.site', 'https://www.tasteitalymenu.com', None, 'http://www.royalpalmsgolfcourse.com', 'http://www.crsth.com', None, 'https://www.cimamedicalcenters.com', 'http://thewayphoenix.com/', 'https://www.tidedrycleanersaz.com/locations/67th-avenue', 'http://www.snapfitness.com/minthill', 'http://www.mexitaco.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://bonnieandclydesrestaurant.com/', None, 'http://www.villageinn.com', None, None, None, 'http://www.activerenter.com', None, None, 'http://www.cornerstoneaz.org', None, 'http://www.callthecatererlv.com/', None, None, 'http://www.pickeringsmiles.com/', 'https://www.dipnailbarhorizon.com', 'http://www.thecornerdeliaz.com/', 'http://www.sohnatural.com/', 'http://thefarmersdaughterflowers.com', 'https://www.popeyes.com', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', None, 'http://www.peterpiperpizza.com', 'http://www.restaurantsoya.com', 'http://www.posiesflowers.com', 'http://www.pizzapizza.ca', 'https://www.haggar.com/stores/aurora-oh', 'https://www.thaispawellnesscenter.com', None, None, None, 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://www.elyatthecurve.com', 'http://www.clevelandwhiskey.com/', '1592931872', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', '1592931882', None, 'https://locator.chase.com/nv/north-las-vegas/5558-camino-al-norte?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.fiatusaofstateline.com', 'http://clarkcountynv.gov', 'https://cobblestone.com/?utm_source=yelp%C3%8A', 'http://sakanayarestaurant.com', 'http://www.charlotteaesthology.com', '1592931915', 'http://kidzpreschool.com/contact/mountainsedgeandsouthernhighlands', None, None, 'http://usvaporoutlet.com', 'http://ses4az.weebly.com/contact.html', 'http://www.menufoodtruck.ca', 'http://www.ajaxpumping.com', 'https://organicpestaz.com', 'https://www.viewpointecenter.com', 'https://www.purebarre.com/location/charlotte-myers-park-nc', '1592931951', 'http://www.punchbowlsocial.com/location/cleveland', 'http://tedcohendpm.com', 'http://www.poolwerx.com/locations/arizona/pool-shop/glendale-85310', 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-82707.html', None, 'http://customer.xfinity.com/service-center-locations?INTCMP=ILC:MA:GEN:GEN552d779b39fd91', 'http://www.10minutemanicure.com/', 'http://www.charlotteroom.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.cremacoffee.ca', None, None, 'http://www.kontourbeauty.com', 'http://www.petsarecool.net', None, '1592932006', 'http://www.dehavens.com/?utm_source=Yelp', 'http://www.achildswardrobe.com', 'http://www.loveleephotos.com', 'http://japanhouse.art.illinois.edu/en/', 'https://www.middletonpolarexpressride.com', 'http://www.birchmount.com', 'http://www.lacoste.com/us', 'https://gymvmt.com', 'https://locations.monro.com/pa/new-kensington/91-tarentum-bridge-rd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://fancyboothaz.com', 'http://fhrg.com/', 'http://www.JimmyJohns.com', 'http://www.galloblancocafe.com', None, 'https://www.energizemassage.today', None, 'http://www.cartergramppdds.com/', 'http://www.northpittsburghoralsurgery.com/', 'http://canyontrailsfamilydental.com/', 'http://www.midlinemotors.com', 'http://www.usps.com/', None, 'http://www.bardis.com', 'https://www.liveatthestewart.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', 'http://thepizzacompany.biz', 'http://www.papajohns.com/', None, 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', 'http://www.DJ-Sterling.com', 'https://imperio-667-mariscos-sushi.business.site', 'http://www.softwaternevada.com', None, None, 'https://lendwithleverage.com', 'http://Www.beatrixbeauty.com', 'https://www.redroof.com/property/pa/monroeville/RRI174', 'http://locations.buffet.com/IL/CHAMPAIGN/0793/index.html', 'https://local.biglots.com/in/madison/255?zcp=pd_local_yelp', None, 'http://www.westside-service-center.com/', 'http://www.thatbbqjoint.com/', None, None, None, None, None, 'http://www.kohls.com/stores/nc/charlotte-250.shtml', 'https://www.grifolsplasma.com/en/-/centralave-charlotte-nc', None, None, None, 'https://order.qdoba.com', None, 'http://www.spoonerphysicaltherapy.com', '1592932187', 'http://www.champaignsurplus.com/', None, 'http://www.kegsteakhouse.com/en/locations/ON/toronto/esplanade-keg/', 'http://chicnailsmadison.com', None, 'http://blissnailbar.com', 'https://milios.com', 'http://www.silverridgespa.com', 'http://www.lowellpumpandwaterlowellnc.com', 'http://www.dfhairsalon.ca', None, None, None, None, None, 'http://www.cleanfreakcarwash.com', 'http://pizzaandbeyond.blogspot.in', 'http://kiddiekampusaz.com/', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/MSNSI', None, 'http://www.thegaminggoat.com', 'http://www.swimkidsaz.com/', None, 'https://www.mallorcacle.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592932283', 'http://willowparkdental.com', None, 'http://www.contemporarywomenscareaz.com', 'http://www.allomoncoco.com', 'http://www.orderosushi.ca', 'https://jimwicklund.com', None, 'http://www.bellistreitsmiles.com', None, None, '1592932322', 'http://www.premierrugwashing.com', 'http://www.lifestylevapor.com', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=101357', 'https://www.mrrooter.ca/north-york', 'http://www.greatcanadianbagel.com', None, 'https://www.uedaphotography.com', None, None, 'http://pawplay.net/', 'http://www.hoffmanrefrigeration.com/', None, 'https://www.naturopathicgroup.com', 'http://thejohnbar.com', 'http://www.fx-tactical.com', 'http://www.accurateenergymanagement.com', '1592932380', 'http://www.cpk.com/location/details/Fashion-Show-Mall', None, 'http://danceacademynorth.com/', None, 'http://www.mtsounds.com', 'http://www.brettsautoservice.com', 'http://www.vegasvacuumsewing.com', 'http://www.sobeys.com/en/stores/sobeys-abbey/', 'http://www.hannahscafe.com', '1592932418', 'http://www.sweetbasilpanasian.com', None, None, 'http://www.serenitywaxandspa.com', 'http://www.stclairveterinary.com/', 'https://www.hilton.com/en/hotels/cltaiht-home2-suites-charlotte-airport/?SEO_id=YELP-HT-CLTAIHT', 'http://galileobreadandcoffee.com', 'https://www.mgmgrand.com/en/amenities/grand-pool-complex.html', 'http://dalatphovegas.com', 'http://www.royaltycleaning.ca/', 'http://local.dmv.org/wisconsin/dane-county/madison/2001-bartillon-drive/dmv-office-locations.php', 'https://www.thelangston.com', 'https://www.renewflooringohio.com', 'https://sundiallocksmith.com', 'http://www.goldenspoon.com', 'http://bonkerzcomedyproductions.com/locations/the-louie-anderson-show', None, 'https://www.homedepot.com/l/Ray-Road/AZ/Chandler/85226/476?cm_mmc=seo-yelp&', None, 'http://mesaroofingcontractor.com', None, 'https://www.papajoessubs.com', None, 'http://www.austinsaz.com', 'http://www.aaaautosales.ca', '1592932506', 'http://theexchange.com', 'https://www.signaturestyle.com/locations/nc/concord/famous-hair-shoppes-at-davidson-corner-haircuts-61130.html', None, 'http://www.whasn.com', 'https://reliableimportsllc.com', 'http://www.PetCremationLasVegas.com', 'http://asiaonerestaurant.weebly.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/9931+Gilead+Road-Huntersville-NC-28078/storeid=2563?cid=ps_ylp_2020', 'http://www.bdmcustoms.net', 'http://www.reeseswigs.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.target.com/sl/chandler-south/2747', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://clickserve.dartsearch.net/link/click?lid=43700044282956305&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', '1592934454', 'http://www.samsonheatingandcooling.com/', 'https://locations.theupsstore.com/ca/concord/1647-willow-pass-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.salonvirtu.net/', None, None, 'http://www.sallybeauty.com/', None, 'https://www.caesars.com/paris-las-vegas/things-to-do/napoleons-lounge?utm_campaign=yelp&utm_source=yelp&utm_medium=yelp&utm_term=NapoleansLounge&utm_content=entertainment', 'https://agents.farmers.com/az/gilbert/nathan-summers?SourceID=AMPALFYEAG&utm_medium=Local&utm_source=Yelp', 'http://www.muchoburrito.com/', 'http://tealabcle.com', 'http://www.electrichairstudio.com', 'http://www.jamacametan.com/', None, None, None, 'http://www.sevabeauty.com/location/nv/las-vegas-west-tropical-parkway/', 'http://www.OTGexp.com', 'http://www.healthmaxphysio.com/thornhill', 'http://www.elephantvapor.com', None, 'http://www.facebook.com/SuttonHouseCLT', 'http://revitalaz.com', None, 'http://theonehotcookie.com', 'http://www.sportchalet.com/', 'http://mishasdancewear.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/46+Morgan+Road-Hudson-NH-03051/storeid=1175?cid=ps_ylp_2020', 'http://refinedpersonaltraining.com', 'http://www.chilis.ca', None, None, 'http://www.gilbertdogs.com', 'http://www.allthebestfinefoods.com', '1592934571', 'http://arco.com', 'http://www.towninn.com', 'https://www.clvmusic.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/95+Freeport+Street-New+Kensington-PA-15068/storeid=3165?cid=ps_ylp_2020', 'http://kentmingcheng.weebly.com', 'http://www.panerai.com', None, None, 'http://www.torontopubliclibrary.ca/hou_az_wy.jsp', 'http://www.drandrewkay.com/', 'http://www.morrispools.com', 'http://www.wandosbar.com/', 'https://agents.allstate.com/christina-piccirillo-henderson-nv.html', 'https://www.americancampus.com/student-apartments/il/champaign/campustown-rentals', 'http://www.karamia.ca/', 'http://restaurantchristophe.com', None, 'https://www.storage-mart.com/calgary/airdrie/township-road-270?utm_campaign=yelp_paid&utm_source=yelp&utm_medium=paid&utm_content=3301', 'http://www.whasn.com', '1592934626', 'https://www.powerofbowser.com/dealership/directions.htm?selectedAccountId=bowsercollision', None, 'http://seductivebeautynink.com', 'http://www.ombrenailspa.com', 'http://www.canadiantire.ca/en/store-locator/on/bolton-on0.carwash.html', 'https://www.daveandbusters.com/locations/glendale', 'https://www.chick-fil-a.com/stapleydrive', 'http://www.cochranofmonroeville.com/', 'http://www.crossfitapollo.com', 'http://www.wegetmovingllc.com', 'http://www.frontporchgrille.com/', 'http://www.starbucks.com/store/10759/', 'http://healthyhomemkt.com', 'http://www.apria.com', 'http://www.mevamekitchenexpress.ca', '1592934667', 'https://www.pikenursery.com/pike-nurseries-lake-norman', None, None, 'https://www.southstburger.com/location/yonge-eglinton-toronto/', None, 'http://lasgorditasrestaurant.com', 'https://www.modernmarket.com', 'http://www.kirklands.com', 'http://audiologybyhollynguyen.webnode.com', None, None, 'http://www.golfmandarin.com/', None, None, None, None, 'http://www.woodchesternissan.ca', None, 'http://www.classiquemarin.com', None, None, None, None, None, None, 'http://www.wilsonsleather.com/home/index.jsp', '1592934727', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/15474+West+Greenway+Road-Surprise-AZ-85379/storeid=5477?cid=ps_ylp_2020', 'http://www.advanced-vision.org', None, 'https://www.abramseyeinstitute.com/locations/las-vegas/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-lasvegas&utm_content=website', 'http://pianomoveraz.com', None, 'http://www.mystudio.net', 'http://www.canarytravel.com/', 'http://www.oncalldentalglendale.com', 'http://99only.com/store/L.V.---Craig/', None, 'https://www.haircutmenmonroevillepa.com', None, 'http://www.swisschalet.com', 'http://www.familyfirstphysicians.com', 'http://www.desertwindcoffee.com', 'http://upstylebrowandbeauty.com', 'http://www.greenplanetcleaning.us', 'http://www.belvoirpethospital.com', 'http://fortmillgoldenchina.com', 'https://www.lifetimefitness.com/spa/spa-salon.html?utm_source=yelp&utm_medium=directory&utm_campaign=SML-acquisition', None, 'http://www.harbourfrontdental.com', None, 'http://www.sexxyespresso.com', 'http://kulaindustries.com', 'https://www.choicehotels.com/arizona/phoenix/sleep-inn-hotels/az805/rates', 'http://www.cowboyscasino.com', None, 'http://redbloom.ca', 'https://northpole.dance', 'http://www.bigalscanada.com/Stores/Locations/Scarborough/scarborough.html', None, 'http://www.repurposedforyou.org', '1592934812', 'http://www.tasteofnaples.ca', None, 'http://lasvegascarmaintenanceshop.com', 'http://www.restaurantmonza.com', 'http://ccsmesquitebroiler.com', 'http://www.kimsnature.ca', None, 'http://www.runningroom.com', None, 'http://www.virgincheese.com', 'https://www.vapesupplycolasvegas.com', 'http://www.mysunwest.com', None, 'http://www.stevenjonesrealty.com', 'http://www.monasroti.com', None, 'http://www.bloombakery.com', None, None, 'http://b2bxpressautobody.com', None, 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'http://bbfamilyhair.com', 'http://www.prolotherapyphoenix.com', 'https://www.chick-fil-a.com/rossparkmall', 'http://robertostacoshop.com', 'http://cafephixmidtown.com', 'http://www.flowerama.com', 'https://union.wisc.edu/dine/find-food-and-drink/der-rathskeller', None, 'https://bartolicleaners.com', 'http://www.vocellipizza.com/swissvale_pa', 'http://www.southpointcasino.com', 'http://www.thaithaitakeout.com/appetizers.html', 'http://quickycarwash.com', 'http://www.drpogue.com', 'http://www.timhortons.com', None, 'https://www.tileshop.com/store-locator/robinson.do', 'http://www.RitasofSurprise.com/', 'http://www.drivepetty.com', 'http://www.salonboutique.net', 'http://popeyes.com', 'http://www.emccomputers.biz', None, 'http://www.laureloakfarm.net', 'https://www.bestwestern.com/en_US/book/hotel-rooms.52031.html?iata=90000019&ssob=BLSSH0005G&cid=BLSSH0005G:yelp:businessurl:52031', '1592934933', 'http://www.dennys.com', 'http://www.redrockvapor.com', 'http://www.armynavysuperstores.com', 'http://motorcitycafelasvegas.mybistro.online', None, 'http://www.protogym.com', 'http://www.eyeandcosmeticsurgery.com', 'https://www.tacobell.com/food?utm_source=yelp&utm_medium=social&utm_campaign=yelp-pilot-test-menu-static-1-CS&utm_content=paid', 'http://www.stonemillbakehouse.com', 'http://schools.ccsd.net/bonanza/', None, 'http://www.EVOMS.com', 'http://www.starbucks.com/store/17649/', 'https://www.sonoraquest.com', 'https://www.dermatologyforanimals.com', None, 'http://www.auntieannes.com', 'http://www.wimpysdiner.net', 'https://petstore.gratefuldogbakery.com', 'http://www.GoldenHawaiianBBQ.com/', 'http://alexanderplace-apts.com', None, 'http://www.familydollar.com', 'http://www.neruda.ca', None, 'http://www.summerlink.com/?s=mesapark', 'http://www.clubcharlestonlv.com', 'http://www.rocknrollfingers.com/', None, 'http://www.lonetreetavern.com', 'http://www.partycity.com', 'http://www.petalk.com', 'https://www.circlek.com/store-locator/us/henderson/3113-hwy-41-n/m0095', 'http://thesouppot.com/', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=3248', 'http://www.moeallenautobody.com', 'http://www.petplanethealth.com/stores/mountainside-plaza-ahwatukee', 'http://www.azdeq.gov', 'http://www.charlotteskinandlaser.com/', 'http://www.hellofresh.ca', 'http://www.lifeissweet.ca/', None, None, 'http://www.stripclubtoronto.com', 'https://locations.popeyes.com/oh/north-olmstead/11805/', 'http://www.momedtrans.com', None, 'http://www.madisonpubliclibrary.org/alicia-ashman', 'https://littlecaesars.ca/en-ca/stores/47910201/499-main-street-south/brampton/on/about', '1592935086', '1592935091', 'http://www.sunsetlandingapartmentsaz.com', None, None, 'http://royalwindsorpub.com', 'http://www.mysolaireapartments.com', 'http://www.allaboutyousalonspa.com', None, 'http://www.mcdowellsonoran.org', '1592935120', None, 'http://www.oreillyauto.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___goodyear_palm_valley', 'http://www.cleanital.com/', 'https://mountainsidefitness.com/locations/scottsdale-shea/', 'http://www.raynewater.com/phoenix/', None, 'https://www.bonafide-restaurant.com', 'https://www.flemingdonparkgolfclub.ca', None, None, 'http://www.blackearthfloral.com', 'http://firstcolumnliving.com', 'http://www.inventoryadjusters.com/', None, None, None, None, None, 'http://www.amayaexpress.com/', None, None, 'http://www.sonicdrivein.com/', 'https://stjames-pt.com', None, 'https://finestremoderngastronomy.com', 'http://www.spirithalloween.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://towing-calgary.ca/', 'http://www.sobeys.com', None, 'http://www.fidelity.com', 'https://www.dragonflynailspa.com', 'http://www.islandmix.ca/pickering/', 'http://artificebarlv.com', None, 'http://www.djssmokeshop.org', 'http://winchellspub.com', None, 'https://www.crustrestaurants.com', 'http://www.outback.com/locations/pa/monroeville', None, None, None, 'http://www.listwithrandy.com', 'http://locations.saksoff5th.com/en/las-vegas-south', 'http://warmspringsdentist.com', None, None, None, 'http://www.pescaderiaenmesa.com', 'http://crossfitmetric.com', 'https://www.chick-fil-a.com/arboretum', 'http://www.rocknrollz.com/', 'http://www.hisshosushi.com', 'http://guildwoodtearoom.ca/', 'http://www.22churchbistro.com', 'http://www.energytanning.com/', None, 'http://www.hermanpangmd.com', None, 'http://www.centurylink.com', '1592935340', None, None, 'http://popeyes.com/find-a-popeyes/?q=L4K+0A4&c=CA', 'http://www.rutledgecleaningservices.com', 'http://www.dragonz.ca/', 'http://filmoreapts.com/', 'http://amazingflowers.bloomnation.com/', None, 'http://www.bathroomredesignandrepair.com/', 'http://montereydrycleaners.com', None, None, 'http://www.bodymason.ca', 'http://www.decaturautoelectric.com', 'https://www.drjeffmoxley.com', '1592935395', 'http://www.jeffreysmithsalon.com', 'http://www.vintnershill.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044282947950&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://vomfasslasvegas.com', 'http://lakeshore2364.braiseryy.com/', 'http://cmacus.com', None, 'http://www.thecleaningauthority.com/eastvalley', None, None, None, 'http://www.mongosgrill.com/', 'https://vegasslidingdoorrepair.com', 'http://www.t-mobile.com', 'http://www.labonitadulceria.com', None, None, None, 'http://www.whatthefriesclt.com', None, None, 'http://www.arboretumobgyn.com', 'http://loganandfinley.com/', 'http://www.kensingtoncornerstone.com/', 'http://www.threeriverstattoo.com', 'https://www.vegasplumbingservices.com', 'http://www.laketowne.com', None, None, None, 'https://www.dairyqueen.com/us-en/locator/Detail/?store-id=12083&localechange=1', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.stellaandshay.com', 'https://www.xceljanitorial.com', 'http://www.scottsdaleappraisalspecialists.com/', 'http://www.kingsfamily.com', 'http://www.kidsbookbank.org', None, 'https://www.anytimefitness.com/gyms/288/Las-Vegas-NV-89139/?utm_source=yelp&utm_medium=local', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCDT', None, 'http://www.earthrosedale.com', None, 'https://vincesautomotiveserviceinc.com', 'http://transcendencefitne.wixsite.com/personaltrng', 'http://www.all6senses.com', None, 'http://www.exploreflipside.com', None, None, 'https://agents.allstate.com/jason-thorpe-gilbert-az.html', 'http://mcmanusauctions.com', 'http://www.sushikanda.com/st-leacuteonard.html', 'http://www.sleepnumber.com/?utm_term=CTA&utm_campaign=mQeEGTOvKLg9V7WcgMYMOQ&utm_source=Yelp&tag=904825&utm_medium=CPC&cm_mmc=Yelp-_-Yelp-_-WebsiteLink-_-mQeEGTOvKLg9V7WcgMYMOQ-904825', 'http://www.wattsrestaurant.com', 'https://www.amf.com/location/amf-desert-hills-lanes?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'http://yourspacesalons.ca/nrg', None, None, 'https://www.sprint.com/locations/nv/las-vegas/3531-s-rainbow-blvd', '1592935599', 'https://www.amctheatres.com/movie-theatres/phoenix/amc-arizona-center-24?utm_uid=yelp', 'http://www.pizzeriaviamercanti.ca/', None, 'http://www.drdarian.com', None, 'http://www.trendfashions.info', None, None, 'http://www.demetriosbride.com', None, 'http://crunchbistro.com', 'https://www.huntington.com/Community/branch-info?locationId=9826', None, 'http://www.amenzone.com/locations/az/phoenix-biltmore/', 'https://locations.arbys.com/us/sc/clover/511-nautial-dr.html', 'https://www.ncautoauction.com', 'http://cloudslingers.com', '1592935657', 'http://www.10catawba.com', 'http://KumaSnowCream.com/', 'http://www.uniquewoodworking.com', 'http://www.loveyogurtusa.com/', 'http://www.centrodesaludfamiliar.com', 'http://www.gourmetgringos.com', 'https://www.rosatispizza.com/location/ocotillo-az/', None, 'http://www.glendaleroofing.com', 'http://www.cobsbread.com/local-bakery/kingsland-calgary', 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', None, 'http://www.gianteagle.com/', None, None, None, 'http://www.theguysplace.com/location-details.php?q=49', 'http://www.gokarttoronto.com', 'http://aerosportsparks.ca/oakville/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://www.fiveguys.com', 'http://bikesonwheels.ca', 'http://uptownloft.com', None, None, 'http://www.americanpave.com', None, None, None, 'https://store.vioc.com/nv/las-vegas/9631-trailwood-dr-89134-HC0003', None, 'https://www.bakerbros.com/visitus', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/LASFF', None, None, 'http://www.nathansfamous.com/', None, None, 'http://www.oakvillegroceryarizona.com', None, None, 'http://www.9round.com/kickboxing-classes/nc/cornelius', 'http://www.quiktrip.com', 'https://desertfinancial.com', 'http://www.movephoenix.com', 'http://www.fantasticsams.com', 'http://www.marinello.com/', 'http://www.greatclips.com/', 'http://www.lunchboxwax.com/henderson/', 'https://la-coppa.com', 'http://www.slimans.net', 'http://www.millikenvet.com', 'http://demetres.com', 'http://www.westworldcanada.com', 'http://yongefrontdental.com', 'http://www.mcso.org', 'http://pizza.dominos.ca/Markham-Ontario-10393', 'http://mrgreek.com/oakville', 'http://www.mcbrideservices.com', None, None, '1592935857', 'http://www.greenhousejuice.com', 'http://www.azmobiledetailandwash.com', None, 'http://treewiseaz.com', 'http://thebulldogpub.com', None, None, 'http://www.arcadiawalk.com', 'http://actionrideshop.com', 'http://www.sassoon-salon.com/en/salon/us/salons-(1)/scottsdale', None, 'https://dabella.us/location/phoenix/', '1592935901', 'http://www.firstoptionlandscape.com', 'http://www.motorcarsvolvocars.com', None, 'http://www.canyoncreektoyota.com', None, None, None, 'http://VanishingInches.com', 'http://www.archerstowing.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.butterchickenroti.com', None, '1592935946', 'https://www.srgseniorliving.com/communities/scottsdale-az-maravilla', 'http://www.mrvacandsewaz.com/', 'http://www.shopboem.com', None, 'http://www.mmmuffins.com', 'http://haaswellnesscenters.com/', 'https://www.thedogandtiger.com', 'http://www.manawerx.com/', None, None, None, 'https://www.hotel89toronto.com', None, 'http://www.AllStateServiceGroup.com', 'http://www.bathandbodyworks.com/home/index.jsp', 'http://www.autobell.com', 'http://www.quesada.ca', 'https://www.libertytax.com/income-tax-preparation-locations/15215.html?utm_source=Yelp&utm_medium=organic', 'http://www.snowappliance.com', None, 'http://www.fantasticsams.com', 'https://www.pret.com/en-us', None, None, None, 'https://www.westjet.com/en-ca/index', None, None, 'https://locations.theupsstore.com/az/mesa/2753-e-broadway-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://lamexicanacantina.com', 'http://www.roexaz.com', None, 'http://www.yourlaziza.com', 'http://www.azcaninecenter.com', 'http://www.nailcouturecavecreek.com', None, 'http://www.napavalleyvet.com/', 'http://www.treelogicllc.com', 'http://www.vaemesa.com', 'http://www.MagicThimbleAlterations.com', 'http://www.birriaqueen.us', 'http://www.agnevada.com', 'http://advancedautoserviceandtire.com/tires-auto-repair-scottsdale-az-3', 'https://www.walmart.com/store/1380/las-vegas-nm/details', 'https://www.thestoutmonk.com', None, None, 'http://www.pawnnowaz.com/locations/mesa-85207/', 'http://www.pasqualespizzeria.com', None, None, None, 'http://www.tuckertirephoenix.com', None, 'http://www.hilandscigars.com', 'http://www.calgaryfamilymd.com', 'http://frascati.ca/', 'http://www.mykolachi.ca', 'http://buttonsnbowspeoria.com/portal/', None, 'http://www.salontestarossa.com/', 'http://www.dior.com', 'http://www.newjumbochinese.com', 'http://PainStopClinics.com', None, None, None, '1592936190', None, 'http://platisdrycleaners.com/', 'http://www.saloncaramia.com', 'http://www.ronjonsurfshop.com', 'https://www.bobevans.com/our-restaurants/locations/80?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', None, 'http://www.greulichsautomotiverepairpeoria.com', None, 'https://locator.chase.com/oh/lyndhurst/5332-mayfield-rd?jp_cmp=rb/LocalListings/aff/branch/na', None, None, None, 'http://tjmaxx.com', 'http://pizzadecasamoon.com', 'http://www.terribleherbst.com/', 'http://www.wintzellsoysterhouse.com/location/pittsburgh-pleasant-hills/', None, None, 'https://www.liveurbanconnected.com', 'http://www.huntercanine.com', 'http://grandmontecitovet.com/', None, None, 'http://www.randkhvac.com', 'http://www.toronto.ca/parks/island/summerschedule.htm', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.preciousslut.net/las-vegas-precious-slut.html', 'http://www.sunshinelaundryservice.com', None, 'http://www.esbiintlsalon.com', None, 'http://www.mattressfirm.com', None, None, 'http://crustrestaurants.com/crust-scottsdale', None, 'http://www.scholarschoice.ca/sc-toys.html', None, None, None, 'http://www.maisonducheddar.com/index.html', 'http://www.comoencasa.ca', 'http://www.begalleries.com/begalleries.html', None, 'http://www.acsolutionsinc.net', 'https://glimpselash.com', 'http://mannsmovingandhauling.com', 'http://www.northbound.com', 'http://www.nascair.com', 'https://enix.beer', None, 'http://www.betseyjohnson.com', 'http://phoenixlocksmithservice.org', None, None, None, 'http://www.charlottematchmakers.com', 'http://www.702-homes.com', 'https://www.supercuts.com/locations/pa/gibsonia/northtowne-square-haircuts-80275.html', 'http://www.JimmyJohns.com', 'http://www.northyorkdentalclinic.com', None, None, None, 'https://ivnutritionnow.com/phoenix-iv-therapy/', 'http://www.pitapitusa.com', 'http://www.khourysfinewine.com/', None, None, 'https://www.northerntool.com/stores/charlotte-north-carolina.htm', None, 'http://www.goldenstatestorage.com/self-storage/nv/las-vegas/golden-state-storage-tropicana', 'https://www.ediblearrangements.com/Stores/1347-Boston-Post-Rd-Madison-CT-06443', 'http://www.arizonabiltmore.com/spa', 'http://www.chocolatsleonidas.ca', 'http://www.calgarytransit.com', 'http://www.tattoomadison.com/home.html', None, 'http://www.azpianotuning.com', 'https://www.carwashnortholmstedoh.com', 'http://www.kiyoshibistro.com', '1592936453', 'http://www.pbbell.com', None, 'http://www.mccrackenautoservice.ca', None, 'http://www.midas.com/cleveland/store.aspx?shopnum=6205&dmanum=212', 'http://www.dennisuniform.com', None, 'http://pinkplumbingandsewer.com', '1592936483', None, None, 'http://www.simpleglowbyjc.com', 'http://locator.shell.us', None, '1592936500', 'http://www.bedbathandbeyond.com', 'http://sonoranexpresscarwash.com', 'http://www.alanasflowers.com', None, 'https://www.aspensquare.com/apartments/nevada/las-vegas/v-lane-apartments?utm_source=Yelp&utm_medium=Yelp', 'http://www.goodlifefitness.ca', None, 'http://www.citymarketdeli.com', 'http://www.effmech.com', 'http://www.starbucks.com/store/9334/', 'http://www.energylifewellness.com', 'http://www.morriscostumes.com', 'http://www.frysfood.com', None, 'http://www.heavenskaffee.com', 'http://www.flowers2005.com', 'http://www.ominkgallery.com', 'https://www.imageandframe.com', 'http://www.marriott.com/hotels/hotel-information/restaurant/phxbd-renaissance-phoenix-downtown-hotel/', None, 'http://richmondheightsautorepair.com', 'http://www.unlimitedcoffee.com', 'http://dentaldigest.com/', 'http://dcpasta.danteboccuzzi.com/', 'http://pawnprivate.com/', 'http://www.aaautocareplus.com', 'http://www.hootersarizona.com', 'http://www.sheerheaven.us', 'http://www.valleyeyecareaz.com', 'http://www.bridgehouseamerica.com', 'http://www.cheztonyspizza.com', 'http://drbaiko.com', 'http://abbotteyecare.com/', 'https://myfountainsfamilydental.com', 'http://www.tekgalaxy.com/', 'http://www.justgates-phx.com', 'http://www.ericksonrealtygroup.com', None, 'http://www.ups.com/', 'http://www.blueskypest.com', 'http://universitydentist.com', None, None, 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'http://www.blunoir.com/', None, None, None, 'http://www.horizontalbooks.com', 'http://www.tkdpride.com/#!blank/xiomq', 'http://www.pitapitusa.com/', None, None, None, None, None, '1592936675', 'http://jonesautotire.com', 'http://www.hardees.com', None, None, None, None, 'http://www.jeremythedogwalker.com', 'http://www.lasvegashabitat.org', 'http://Iphixation.com', 'http://www.asapaz.com', 'http://dreamcyclery.com', None, 'http://www.timhortons.com', 'https://www.dominos.com', 'http://www.greystonevethospital.com', 'https://azdesertent.com', 'http://henderson.tdslib.org/', None, 'http://www.baskinrobbins.com/', 'https://locations.wafflehouse.com/sc-clover-1957', 'http://www.powerofbowserhyundai.com', 'https://www.wyndhamhotels.com/hotel/08511?tel=18005369326&iata=00093785&cid=fe:se:20170424:yl:pp:seus:08511', 'http://www.flirtcustomlash.com/', 'https://federicosmexicanfood.com', 'https://www.olivegarden.com/locations/az/surprise/surprise/1627?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:surprise-az-1627_pl:locurl_rd:1488', None, None, 'http://www.caminocleveland.com', None, None, 'http://discreplay.com/champaign.php', 'http://www.cornerarchery.com', 'http://www.volutone.com', 'https://www.signaturestyle.com/locations/on/pickering/first-choice-haircutters-51159.html', None, None, 'https://haircutmenscottsdaletownecenter.com', None, 'http://www.algsn.com/', 'https://www.cantina15eleven.com', 'https://www.northwestcareercollege.edu', None, 'http://www.medinavisionandlaser.com', 'http://www.theperioplace.com', 'http://www.marcallenortho.com', 'http://Www.lezizkitchen.com', None, None, 'http://www.acehardware.com/store-details/05037', 'http://www.restoredane.org/', 'http://kaleidoscope.love', None, None, None, 'http://www.webster-ortho.com', 'http://www.NutritionWorks.Vegas', 'https://www.mcgranitecharlotte.com', 'https://www.lifewater.solutions', 'https://www.canadianappliance.ca/Showroom/Canadian-Appliance-Source-Toronto-North-York-Scarborough', None, 'https://www.storagewest.com/facilities/buffalo-drive/?utm_medium=organic&utm_campaign=yext&utm_source=yelp', None, 'http://pearldentalaz.com', None, '1592936884', 'https://www.mydrnow.com', 'http://mintskincaresalon.com', None, None, 'http://www.simplydivinelmt.com', 'http://www.tigerdirect.ca', 'https://www.squaretrade.com/go/locations/cleveland?utm_campaign=cleveland&utm_source=yelp.com', 'http://www.philippelusi.com', 'http://www.dentistryoftoronto.com', None, 'http://www.hotbunzz.com', 'http://www.regalnails.com', None, 'https://www.rwmloans.com', None, None, 'http://www.veggiedelight.biz', 'http://clickserve.dartsearch.net/link/click?lid=43700044282956245&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.vinnysky.com', 'http://www.jacquelinesuzannes.ca', 'http://whitedovethrift.org', '1592936958', None, 'http://www.azeah.com', 'https://www.purebarre.com/location/las-vegas-nv', '1592936969', 'http://fuegobistro.com', None, None, 'http://www.thelabsalonspa.com', None, 'http://www.villagesmilecare.com/', '1592936993', 'http://www.gotusfit.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, 'http://www.timhortons.com/', 'http://www.shuku.ca', 'http://www.essentialwellnesscenters.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.railyardtap.com', None, 'https://calibercollision.com/locate-a-caliber-collision-center/charlotte-tyvola-rd', 'https://www.officedepot.com/storelocator/nv/las-vegas/office-depot-3351/', None, None, 'http://www.themapletreecafe.com', None, '1592937047', 'http://theclaytonvenues.com/venues/the-clayton-house/', None, 'http://macylanebecker.signaturenv.com', 'https://www.fragranceoutlet.com/pages/designer-fragrances-las-vegas-premium-outlets-south-24', '1592937064', 'http://www.socialtappub.com', None, 'http://montecarlo.com', 'https://www.briandebrunlaw.com', 'http://www.caseys.com', 'http://lacarnita.com/', 'http://www.bristolbombay.com/', None, None, None, 'https://cfo.asu.edu/ubs-passport?destination=node%2F16939', 'http://www.mononapizzaoven.com', 'http://www.cuairductcleaning.com', None, 'http://www.elrinconwadsworth.com', 'https://mypopcornkitchen.com', None, '1592937124', 'https://www.covenantcare.com/stores/silver-ridge-healthcare-cente/', 'http://www.rockstargallery.net', 'http://www.eliteplumbingac.com', 'http://extremebordersandcurbsaz.com', None, '1592937140', 'https://www.wyndhamhotels.com/hotel/18164?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:18164', None, None, 'http://www.harpersnursery.com', None, None, 'http://www.lvacheer.com', 'http://www.hennashoppe.com/locations/downtown-tempe', 'http://promotionptaz.com/index.php', None, None, None, 'http://thedonutbouquet.com', 'http://www.blazeshops.com', None, None, '1592937195', 'http://www.azcleanpros.com', 'https://www.danielsjewelers.com/Online_Application_Starts.cfm', 'https://bhrcenter.com/location/med-spa-summerlin/', 'http://www.allstar-materials.com/Homepage.html', 'http://www.majorappliances.ca', 'http://www.whodoesyournails.com', 'http://www.showhome-furniture.com', None, None, 'http://www.iloveindoorsoccer.com', None, 'https://www.mkdlasvegas.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.allmobilematters.com/stores/superstition-springs/', 'http://www.petzplace.com/', 'http://landofwine.com', None, None, 'http://www.shellminimart.com', 'http://franktuary.com/mobile/location-mobile/', 'https://locations.theupsstore.com/az/tempe/1753-e-broadway?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://leesliquorlv.com/locations/lake-mead-tenaya-2/', None, 'http://www.randyspatties.com', None, 'http://www.atlwings.com', None, None, 'http://www.fountainhillsrestoration.com', 'http://www.austinsbar.com', 'http://www.phoenix.pizza', 'http://www.lasvegashomes.com', 'http://www.commercialcleaninglv.com', 'http://www.JimmyJohns.com', None, 'http://www.greatclips.com/', '1592937317', 'http://www.goodearthcafes.com/locations/alberta/airdrie', None, '1592937325', 'http://www.fourpointsclevelandairport.com/dining', 'http://yourhealthyfutures.com', '1592937338', 'https://www.redmountainweightloss.com/arrowhead/', None, 'http://www.dentaldstudio.com/glendale', 'http://numeroussushi.business.site', 'https://azlaserdentistry.com', None, 'http://www.foundrehotels.com', 'http://www.benwickspub.com', None, 'http://www.unionoralsurgery.com', 'http://www.Blairscustomcakes.shutterfly.com', 'http://www.victoriassecret.com', None, 'http://kendaladj.com', 'http://www.azpooltime.com', 'http://empireworks.com/', 'http://www.gtaphotographyclasses.com', None, None, 'https://johnhancockcontracting.com', None, 'https://www.storagewest.com/facilities/craig-road/?utm_medium=organic&utm_campaign=yext&utm_source=yelp', 'http://www.commonsort.com', 'http://www.starbucks.com', 'http://www.qualityinsurancelv.com', 'https://www.speedeeoil.com/locations/fort-mill-sc-9310/', 'http://btskoreanbuffetrestaurantlasvegas.favorite-cafes.com', None, 'http://www.animalkingdomaz.com/', 'http://www.merhipsy.com', None, None, 'https://www.completecare.org', 'https://bananarepublic.gap.com', 'https://www.dayford.com', 'http://locations.truereligion.com/nv/las-vegas/51013/', 'https://www.teslamotors.com/findus/location/service/scottsdale', 'https://www.grandcanyondestinations.com', 'http://aimorders.com/', None, 'http://www.turkishk.com/', 'https://www.hendricklexuscharlotte.com/?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, None, 'http://kristapsons.com', 'http://www.thepizzabuffet.com/', 'http://www.cashamerica.com/SUPERPAWN-stores/NV/LASVEGAS/LV12', 'https://www.jaleo.com/location/las-vegas/', None, 'http://www.mumbaisapphire.net', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://desertdentistry.com', 'http://www.sdtacofactory.com', None, 'http://www.zracing.ca', None, None, None, '1592937543', 'http://www.sdsdental.com/', 'https://kabutos.com', None, 'https://stores.theory.com/1159408-theory-las-vegas', 'http://fracturedprune.com/location/glendale-az', 'http://elpacificoseafood.com', 'http://www.chilinoodlecorner.com/', 'http://www.ricssmokehouse.com', None, None, 'http://www.superiorhardwoods.com', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=1', 'https://poppyseedsbagels.com', 'http://marben.ca', 'http://www.cornerbakerycafe.com', 'http://Vegas.kw.com', 'http://broastinn.com', None, None, 'http://qdoba.com', 'http://www.myrivertowne.com', '1592937625', None, 'http://phoenixeyebrows.com', 'http://sweetfrog.com/locations/store/sweet-frog-white-hall-commons-charlotte-nc', None, 'http://www.volvometrowest.com/', 'http://www.floorsourceaz.com', 'http://www.desertparking.com/', 'http://business.google.com/website_shared/launch.html?f=bobs-vape-smoke-shop.business.site', '1592937657', 'https://www.homedepot.com/l/S-Boulevard-Charlotte/NC/Charlotte/28217/3646?cm_mmc=seo-yelp&', None, None, 'http://www.firstchoicemoving.com', 'http://chopchopchinesekitchen.com', 'http://www.dtndesign.com', '1592937679', 'http://parkroad.duckworths.com', 'http://locations.michaels.com/IL/PEORIA/2025/', 'http://Dulceardor.com', 'http://www.lasikplus.com/location/chandler-lasik-center/?encSource=12149&cmpid=sem_189', 'http://www.thebandr.com', '1592937698', None, 'http://carrington.edu/schools/mesa-arizona/?LeadSrcID=1176&AdvGroupName=Yelp&AdvCampaignName=YelpPhoenixFY17&AdvSource=Internet', 'http://www.jumpersjungle.com/peoria/', None, 'https://www.firehousesubs.com/locations/az/crossroads-at-tolleson', None, 'http://www.GolfDragonRanch.com', 'http://www.pspassoc.com', 'http://www.charvan.com', 'http://www.phoenixpubliclibrary.org/Locations/Pages/Century.aspx', None, 'http://www.otaninoodle.com', None, None, 'http://www.villagepaint.hunterdouglas.ca', 'http://www.barbershopintorontoon.ca', 'http://www.mediumrare.to', 'http://www.superettecafe.com', 'https://www.victoriassecret.com/store-locator/store?lat=33.62579&lng=-111.92922&id=1261#/store/1261', 'http://www.meyersautoparts.com/', None, 'https://local.albertsons.com/az/glendale/5040-w-cactus-rd.html', None, 'http://smokespoutinerie.com', None, 'http://www.sultankabob.ca', 'https://www.choicehotels.com/arizona/phoenix/comfort-suites-hotels/az109/rates', None, 'http://www.todayspatio.com/gilbert/', 'http://www.vaporhousestores.com', None, 'http://www.V-12motorsports.com', 'http://sheendayspa.com/c', 'http://theplaypen.ca', 'https://streetfoodsworld.com', 'http://www.thedailyglowcustomskincare.com', None, None, None, None, 'https://www.livingspaces.com/stores/summerlin', None, 'http://www.wrenchauto.com', None, None, 'http://www.enclaveatarrowhead.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', None, None, 'http://pizzaboysshawarma.com', None, None, None, None, 'http://eatcarver.com', 'http://www.littlejewelz.com', 'http://www.dollargeneral.com', None, 'http://www.letitrollskateboarding.com', 'http://www.reginospizza.com', 'https://www.harveys.ca', None, 'http://www.orthopedicarizona.com', 'http://www.elementwheels.com', None, None, None, 'http://www.greatclips.com/', 'http://synergysir.com', 'http://simplysweetnewmarket.com', 'http://www.airparkconsignment.net', None, 'http://www.monarchtheatre.com', None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.hothautehot.net', None, 'http://www.northolmstedcollision.com/', 'https://www.halfmoonsportsgrill.com', 'https://locations.riteaid.com/locations/wa/lakewood/5700-100th-street-sw.html', 'http://www.misshickorystearoom.com', 'http://www.ilpaesanopizza.com', 'http://www.tutortime.com/your-local-school/glendale-az-6081/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, None, 'https://www.moneytreeinc.com/branch/north-nellis', None, None, 'http://www.swisschalet.com', None, None, 'http://atomicagecomics.com', 'http://www.rebehomes.com', None, 'https://www.crookedrivercrossfit.com', '1592938013']
len(urls)

86950

In [10]:
saved = urls
print(saved)

['http://www.therangeatlakenorman.com/', None, 'http://www.felinus.ca', None, 'https://www.usemyguyservices.com', 'http://oasisautocenter.net', None, 'http://junctiontire.net/tires-auto-repair-mesa-az', 'http://www.theempanadashouse.com', 'http://www.xtremecouture.ca', 'https://landscapingcalgary.org', None, 'http://www.chocolateshoppeicecream.com', 'http://www.convertabath.com/', None, 'http://www.desertstorage.com/henderson-nv-self-storage', 'https://www.manoloblahnik.com/in/boutiques/Wynn%20Las%20Vegas', 'http://www.bloomandblueprint.com', 'http://www.2carguyz.com', 'https://fitbodyaz.clickfunnels.com/sales-page-yelp', None, 'https://www.glendaleaz.com/glitters/', 'http://www.ncbrewsmusic.com/', 'http://www.tipsyryde.com', 'http://www.philthyphillys.com', None, None, 'http://www.hendrickmotorsofcharlotte.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, None, 'https://www.apadana.restaurant', 'https://www.iga.net/fr/recherche_de_magasin/magasin

In [11]:
urls[-1], len(urls)

('1592938013', 86950)

In [12]:
delays = [.01,.02,.03,.04,.05,.06,.07]
for i, entry in df.iterrows():
    if i < len(urls): continue
    #time.sleep(np.random.choice(delays))
    #website, yelp_url, blocked = fetch_url_from_yelp_stop_if_captcha(entry)
    website, blocked = fetch_url_from_yelp_stop_if_captcha(entry)
    if blocked == 1:
        print('We are blocked at {}'.format(i))
        break
    #print(i, 'Website not found! Check out: ' + yelp_url if website is None else 'Found: ' + website)
    urls.append(website)

In [123]:
print(urls)

['http://www.therangeatlakenorman.com/', None, 'http://www.felinus.ca', None, 'https://www.usemyguyservices.com', 'http://oasisautocenter.net', None, 'http://junctiontire.net/tires-auto-repair-mesa-az', 'http://www.theempanadashouse.com', 'http://www.xtremecouture.ca', 'https://landscapingcalgary.org', None, 'http://www.chocolateshoppeicecream.com', 'http://www.convertabath.com/', None, 'http://www.desertstorage.com/henderson-nv-self-storage', 'https://www.manoloblahnik.com/in/boutiques/Wynn%20Las%20Vegas', 'http://www.bloomandblueprint.com', 'http://www.2carguyz.com', 'https://fitbodyaz.clickfunnels.com/sales-page-yelp', None, 'https://www.glendaleaz.com/glitters/', 'http://www.ncbrewsmusic.com/', 'http://www.tipsyryde.com', 'http://www.philthyphillys.com', None, None, 'http://www.hendrickmotorsofcharlotte.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, None, 'https://www.apadana.restaurant', 'https://www.iga.net/fr/recherche_de_magasin/magasin

In [124]:
urls = ['http://www.therangeatlakenorman.com/', None, 'http://www.felinus.ca', None, 'https://www.usemyguyservices.com', 'http://oasisautocenter.net', None, 'http://junctiontire.net/tires-auto-repair-mesa-az', 'http://www.theempanadashouse.com', 'http://www.xtremecouture.ca', 'https://landscapingcalgary.org', None, 'http://www.chocolateshoppeicecream.com', 'http://www.convertabath.com/', None, 'http://www.desertstorage.com/henderson-nv-self-storage', 'https://www.manoloblahnik.com/in/boutiques/Wynn%20Las%20Vegas', 'http://www.bloomandblueprint.com', 'http://www.2carguyz.com', 'https://fitbodyaz.clickfunnels.com/sales-page-yelp', None, 'https://www.glendaleaz.com/glitters/', 'http://www.ncbrewsmusic.com/', 'http://www.tipsyryde.com', 'http://www.philthyphillys.com', None, None, 'http://www.hendrickmotorsofcharlotte.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, None, 'https://www.apadana.restaurant', 'https://www.iga.net/fr/recherche_de_magasin/magasin/0293-marche-d-alimentation-beck-inc', None, 'http://www.wetzels.com', 'http://www.beechmontcc.com', 'http://www.gkvapors.com', '1592058805', 'https://www.bannerhealth.com/locations/phoenix/banner-university-medical-center-family-medicine', 'http://www.thegourmetburgerco.com', 'https://www.goodyearautoservice.com/en-US/shop/PA/Pittsburgh/000901034-15206-3149', 'http://stores.disneystore.com/ca/concord/317', None, 'http://meatchix.com', None, None, None, None, 'http://www.basspro.com/', 'https://ccv.church/locations/anthem', 'https://locations.wendys.com/united-states/oh/cleveland/13939-euclid-ave.', None, None, 'http://www.bathandbodyworks.com', 'http://irenestaproom.com', 'http://hingetown.com/', 'http://www.bestitchedneedlepointshop.com', 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=1', None, 'https://www.smlentertainment.com/calgary-north/', None, None, 'http://fiveguys.com/', 'http://platinumkustomz.com/', None, 'http://locations.tccrocks.com/az/gilbert/2218-e-williams-field-rd.html', 'https://local.fedex.com/nc/charlotte/office-0746/', 'http://www.lacoste.com/us/', 'http://www.helenblakeyflowers.com/', None, 'http://localpetpgh.com', 'http://www.ocotillointernalmedicine.com', 'http://www.mpbattingcages.com', 'https://www.garageexperts.com/location/charlotte', None, 'http://redlinepromotions.com', None, 'http://stqitoronto.com', 'http://saxetheater.com/', 'http://www.sincitypartybuses.com', 'http://www.cjaycomputers.com/', None, 'http://www.visitnc.com/listings/view/52079', None, '1592059164', 'http://www.minthillbarbershop.com/', 'http://actionfurnace.ca', 'http://www.mamanapolipizza.com', 'http://www.monarichiebride.com/', 'http://www.movers4less-il.com/', '1592059211', None, 'http://darrochmotorsports.com', 'http://www.jeffersonchandler.com/?utm_medium=listing&utm_source=yelp', 'http://landing.trugreen.com/yelp?city=Champaign&state=IL&zip=61822&utm_campaign=ORGANIC&marketingpartner=9817', None, 'http://fresh.longos.com', None, None, None, 'http://www.rehabdirectives.com', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.tavernrestaurantgroup.com', None, None, 'https://www.pizzaville.ca', 'http://www.royalskincare.net', '1592059367', 'http://www.sugarbowlscottsdale.com/', 'http://www.vikingcleanersaz.com', 'http://www.timhortons.com/', None, None, 'http://www.shalecreekgolfclubggp.com/', None, '1592059436', 'http://store-locator.barnesandnoble.com/store/2147', 'https://www.myairtoday.com', None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-indian-school?utm_campaign=honorhealth-medical-group-indian-school&utm_medium=local&utm_source=yelp', 'http://www.marcos.com', 'http://www.sleepandwellnessctrs.com/index.php/modules-menu/2012-01-19-13-38-38/henderson', 'http://www.hotelcharlotterestaurant.com/hotel/', 'http://www.handandstone.com', 'https://www.ulta.com/stores/charlotte-nc-590', 'http://www.JesusChurch.life', 'http://www.jjspizzacle.com/', 'http://www.dennys.com', 'https://rinsenride.com', None, 'https://kulinaryaexpress.com', 'http://www.ahwatukeepeds.com/', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=100934', None, 'http://www.amegashootingsupplies.com/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, None, 'http://www.freshcoatpainters.com/charlotte', 'http://clk.atdmt.com/HBO/go/165733594/direct/01/', None, 'http://www.hottubliquidators.com', 'https://sharonmtuttle.com/', 'http://www.fleurishflowershop.ca', 'http://www.healthspringlv.net', 'http://www.torontodermatologycentre.com', 'http://chandlersymphony.com', None, None, 'http://www.zavcoffeeshop.com', None, 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=0352&s_cid=lsl0000001', 'http://www.frederickandsons.com', 'http://www.winerack.com', 'http://www.chefalyssaskitchen.com', None, 'https://www.fatmoespizzawings.com', 'http://www.shearsensationsonline.com', 'http://www.movingforwardmadison.com/', None, 'http://www.kegsteakhouse.com/en/locations/ON/toronto/esplanade-keg/', 'https://www.thethingshop.com', None, None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89128/027192/', None, None, 'https://www.target.com/sl/richland-twp-north/2262', 'http://www.fearlessmeat1.com', None, None, 'http://www.qobollabridal.com', None, 'http://www.lcbo.com', 'https://www.dayspascottsdaleaz.com', 'http://leecafesc.com', 'http://www.gofitnessnation.com', None, None, 'https://www.peoriaaz.gov/government/departments/parks-recreation-and-community-facilities/parks-and-trails/pioneer-community-park', 'http://www.nwpoolaz.com', 'http://www.cruffs.com/', 'http://dwellingsinthedesert.com', 'https://agents.allstate.com/oscar-arnold-goodyear-az.html', 'https://www.walgreens.com/locator/walgreens-1725+northport+dr-madison-wi-53704/id=2967', None, 'http://www.purelifeaz.com', None, None, None, 'http://stlouiswings.com', None, 'http://www.massageindavidson.com', 'http://www.aumspatoronto.com', 'http://www.pizzafresh.com', None, 'https://www.raynathans.com', 'http://www.docrequest.com', 'http://www.drsimms.com', None, 'http://www.pitcrewmovin.com', 'http://www.planetfitness.com/gyms/las-vegas-flamingo-nv-611?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://www.jealousyonline.com', 'http://www.communalmule.com', None, 'http://www.thebeautyboutiquewhitby.com', 'http://www.torontopolice.on.ca/museum/', 'http://www.goldstandardhomecare.com', None, 'http://www.103yoga.com', 'https://membercuts.business.site', 'https://dutchbros.com/?utm_source=goodyear&utm_medium=yelp&utm_campaign=website_goodyear', 'http://phxstreetfood.org/', None, None, 'http://www.criminalcustomz.com', None, 'http://standandstair.com', None, 'https://www.mazzeolimousine.com', 'http://dentsquad.ca', 'http://www.menchies.com', 'https://www.smalv.com/OurCenters/HealthCareCenters/Siena', 'http://mystonecreekdentist.com', 'http://www.chobuffet.com', 'http://www.pho.com/mesa-az/pho-hien', 'http://www.mrakovic.com', 'http://www.childtime.com/your-local-school/las-vegas-nv-1803/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, None, 'https://www.sonoraquest.com/find-a-location/scottsdale-scottsdale-rd-mescal/', None, None, None, None, 'https://www.meineke.com/locations/az/surprise-4338/?utm_source=yelp&utm_medium=xvc', 'https://losolivosristorante.business.site', 'http://sunfoodsupermarket.ca/', 'http://www.2uglassandtint.com', 'http://edwardsbeautycle.com', 'https://www.allmysons.com/cleveland', None, None, 'http://www.thetailwaggersclub.com/', 'https://veggiehouse702.com', '1592060496', 'https://www.mr-bills.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://olympiasweettreats.com', 'https://locations.churchs.com/az-phoenix-7235', 'http://MasterMechanicalCleveland.com', 'https://psychbc.com/locations/greater-cleveland/north-olmsted-oh', None, 'http://sevabeauty.com/locations/charlotte_nc', None, 'http://www.uncleotis.com/', None, 'https://www.scottsdaleflighttraining.com', 'http://www.charlotteorthotics.com', None, 'http://www.motherhood.com/shipping.html', '1592060654', 'http://www.shintkd.com', None, 'http://www.thebookshopaz.com/', None, 'http://wandaroche.starkhomes.com', 'http://www.lvchinatownplaza.com/event_index.htm', 'http://www.solissouthline.com', 'http://www.hairrevivalaz.com', 'http://www.pivotimage.com', 'http://kingsfamily.com/?utm_medium=referral&utm_source=yelp', None, None, 'https://www.repairngo.com', 'http://www.fountainhillsrv.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.clubpilates.com/dtphoenix/', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'https://wearernd.com', 'http://www.lcbo.com', 'http://www.skinconceptsspa.com', 'https://locations.tropicalsmoothiecafe.com/nv/henderson/10612-south-eastern-avenue', None, 'http://lvmpd.com/', None, 'http://www.pueblomedicalimaging.com', 'http://www.creditunion1.org', None, 'http://www.pjspet.com', 'http://www.menyhartplumbing.com', 'http://www.cuisinemalaya.com', None, 'http://www.truvapenv.com', 'http://www.shopmadmod.com', None, 'http://www.southwestmobility.com/', 'http://www.wendys.com', 'http://www.starbucks.com/store/9298/', '1592061020', 'http://www.liquorstorevegas.com', 'https://www.hottopic.com', 'http://rubberstampevents.com', None, 'http://www.jcsgrillhouse.ca/mississauga/', 'http://www.guyslock.com', 'https://qcontrary.com', None, 'http://www.thecatsmeow.com', 'https://www.thejoint.com/arizona/glendale/arrowhead-ranch-48016', 'http://www.fruitsnroots.com', 'https://www.maids.com/49/?utm_source=Yelp', 'http://www.td.com', 'https://www.usps.com/', None, 'http://www.airrite-supply.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, 'https://www.subarusuperstorewest.com', 'http://allinonerepairs.us/index.php/home/', 'http://www.joesautoaz.com/', 'http://edulisrestaurant.com/', 'http://www.sdil.net', 'http://www.churchs.com', 'http://www.fatbastardburrito.ca', 'http://www.dollarama.com/', 'http://www.blackod.ca', 'http://www.rupertcornelius.net', 'http://www.alliancelv.com/', 'https://harrymarshlaw.com', 'https://nergysolutions.com', 'http://www.elitefloralevents.com', 'http://www.arizonaexecutivellc.com/', None, 'http://www.dunkindonuts.com', None, None, None, 'https://www.azairtime.com/scottsdale', 'https://www.jasonsdeli.com/restaurants/henderson-deli', None, None, None, 'http://www.izumi-sushi.com', 'http://www.logoexecutives.com', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', None, 'http://climbrefuge.com/', None, 'http://asiancafe.weebly.com/', None, 'https://www.brakesplus.com', 'https://www.churrasqueiramartins.com', None, 'http://www.vernspizza.com', 'http://tatmanstowing.com', 'https://www.mbkseniorliving.com/senior-living/az/scottsdale/mcdowell-village/?utm_source=mcdowell_village&utm_campaign=yelp', 'http://www.dhtorontoairport.com/', None, 'http://www.exxon.com', 'https://www.peacockrestaurants.com', 'http://www.thehousecoffee.ca/', None, 'http://www.calgarycurlingclub.com', 'https://clevelandhabitat.org/restore/', None, 'http://www.revelsalonmadison.com', 'http://www.misterchangs.com', 'http://www.smilesforeverpgh.com', 'http://www.charlotterusse.com', 'http://www.bistrogrande.com', None, 'https://ottogelato.ca', None, 'http://twizted-manez-beauty-barber.business.site', None, 'http://uncletetsu-ca.com', 'http://www.bitesandbrewspittsburgh.com/', 'https://www.walmaneye.com', 'http://speparty.com', 'http://www.propertyclaimadjusters.com/', 'http://www.zandrus.com', 'http://www.mercedesbenzofchandler.com', 'http://www.mycasinoquest.com', 'http://concordhairbeautysalon.com', None, None, 'http://ascentdronevideo.com/', None, 'http://www.cineplex.com/theatres/theatredetails/silvercity-crossiron-mills-cinemas-xscape-entertainment-centre.aspx', None, None, 'http://www.northtaphouse.com', 'http://www.mydcdental.com', 'http://www.kadensnails.com', 'http://soulgastrolounge.com/', 'https://greenvalleyranch.sclv.com/Entertainment/Lounges-and-Bars?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://katespade.com', None, None, None, 'https://www.toronto.ca/data/parks/prd/facilities/complex/1748/index.html', 'https://newresultsmedicalweightloss.com/near-you-scottsdale-arizona/', 'http://saigonnailspa.ca', None, 'http://www.bellevuebeer.com/', None, None, 'http://trufusion.com/', 'https://www.heartwoodroastery.com', 'http://www.poshhairandspa.com', 'http://www.yankeecandle.com', '1592062044', 'http://www.footcare4you.com/', '1592062563', 'http://www.livewellpgh.com', '1592062577', 'http://www.bloombc.com/', 'https://all-season-nails-spa.business.site', 'http://acninc.com', None, 'http://www.rexall.ca/', None, None, 'http://www.brookfieldvet.ca', 'http://theflowerroom.com/', 'http://sichuanren.ca', '1592062673', 'http://www.lodidoor.com', 'https://www.zerodegreescompany.com', 'http://thaimassagepro.vegas', 'http://www.pizzanova.com/locations/markham.html', 'http://www.yelp.com/events/chandler-rockin-taco-street-fest-2', None, 'https://www.purehockey.com/store.aspx?utm_content=Pure+Hockey-Monona-WI&loc_id=85', '1592062748', 'http://www.hickoryridgefirearms.com/page8.php', 'http://www.fantasticsams.com', 'http://www.marcs.com/stores/marc-s-medina-grocery-store-44256.aspx', 'http://www.yd.com/torontoyonge-eglinton/default.aspx', 'http://www.31kitchen.com/InfoEng.php', 'http://www.wamplerapartments.com', 'http://www.enterprisecarsales.com/location/53R1/Enterprise_Car_Sales_Charlotte?mcid=iyp:277&CUR=yelp', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXWH', 'http://www.starbucks.com', 'http://www.chewchew.net', 'http://jmacnv.com', None, 'http://www.gibs.bar', 'http://www.garciasmexicanrestaurants.net/', 'http://www.bobosbarbeque.com', 'http://www.chandlerinnaz.us', None, 'http://www.crescentoralsurgery.com/', 'http://www.fivestarmovingvegas.com', None, 'http://www.she-lv.com/', '1592062917', 'http://www.platinumpaintandbody.com', 'http://www.phxfoot.com', None, 'http://www.az-insulation.com', None, 'http://www.ilovemilanos.com/', 'http://www.duckislandclub.com/', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', None, None, 'http://skippa.ca', None, '1592063032', None, None, 'http://www.spanishoaksapts.com', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.easydrinkeasygo.com', 'http://www.wayneacebusandlimo.com', None, 'https://www.marriott.com/hotels/hotel-information/restaurant/lasbr-renaissance-las-vegas-hotel/', None, None, 'http://karbking.com', None, None, 'http://cooling-az.com', 'https://anniys-massage-spa.business.site', 'http://white-oaks.com/cmswo/', 'http://www.kirstyblattner.com', None, None, None, 'http://www.gap.com?tid=gpme000290', 'http://www.cvrr.com', 'http://www.leelaecospa.com', 'http://www.leakdetectionarizona.com', None, 'http://www.dragonflyhotyoga.com/locations/middleton-west-madison-wi/', 'http://stores.partycity.com/az/goodyear/party-store-pc947.html', 'http://www.1800degrees.ca', 'http://locationsca.michaels.com/qc/saint-laurent/4967/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.chopinrestaurant.com', 'http://www.homedepot.ca', None, None, 'http://www.clemetparks.com/education/facilities/index.asp', 'http://www.bombaybuffet.ca', '1592063291', 'http://www.portagepointe.com', 'http://www.lakeeffectlaundromat.com', None, None, 'https://www.loandepot.com/msander', 'http://xmsengineering.com/', 'http://www.puntogelatotoronto.com', None, 'http://www.rudinospizza.com', 'http://www.mimiscafe.com', 'http://larkandkey.com/', 'https://www.chocolatsfavoris.com', 'http://www.myrotiplace.com', 'http://www.sdmi-lv.com', 'http://www.allcarewellness.com', 'http://www.firstclassvanlines.ca/', 'https://www.honorhealth.com/physicians/peter-ferrara', 'http://www.canyonridgephotography.com', 'http://www.trianglebenefitservices.com', None, None, 'http://www.abrazadental.com?utm_campaign=local&utm_medium=citations&utm_source=yext', 'http://www.lampsplus.com/?sourceid=SMYELPTXLKStore16&cm_mmc=YELP-SM-_-Text-_-Link-_-Store16', 'http://www.wtaetv.com', None, 'http://www.choicechiropractic.net', '1592063514', None, 'http://www.keytohealingmassage.com/', None, None, 'http://www.duquesne.org', 'http://gcglassllc.com', 'https://www.myedgecharlotte.com', 'https://www.pinnaclebankaz.com', 'http://www.johnjayautomotive.com/', 'http://www.barneys.com', 'http://www.torontocoffeeandteahouse.com/', None, None, 'http://timessquareaz.com/', 'http://www.TriPlumb.com', 'http://www.jchobbies.com', 'https://www.adencamera.com', 'http://izakayaju.com', 'http://www.jonesysclassiccleaners.com/', 'http://www.anchorbarcanada.com/square_one/', None, 'http://www.cloudcareclinics.ca', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://bikesauce.org', None, 'http://www.sears.com/stores/arizona/mesa/0001628.html', None, None, None, None, None, 'http://singletrackfactory.com', None, 'http://www.residentialREclosings.com', 'http://www.sharifian.com', None, None, '1592063785', 'http://heritageeyecare.ca/', 'http://chazandodette.com', None, 'http://www.usa-autotransport.com/Phoenix', None, 'http://www.celebritytanning.com', 'http://www.blissdentallv.com', None, None, 'http://reinholdresidential.com/shadysidecommons/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.littlecaesars.com/', None, None, 'http://www.pods.com/phoenix.aspx', 'https://combatzonepblv.com', 'http://www.arizonawalkshop.com/', 'http://drakegeneralstore.ca', None, 'http://www.redhotrobot.net', None, 'http://miragenailsandspa.webs.com', 'https://www.mgmgrand.com/en/nightlife/whiskey-down.html', None, 'http://www.asianbuffet328.com/', 'http://www.nstuffmusic.com', 'http://www.groovyshoes.ca', 'http://www.gotoguyshandyman.com', 'http://www.meltingpot.com/charlotte-lake-norman/welcome', 'http://www.space55.org', None, 'http://fahhairextensions.com', 'http://www.visionsourcewilliamfharveyod.com', None, 'http://www.eggsmart.ca', 'https://www.lvatv.com', None, 'http://www.historybygeorge.com', '1592064139', 'http://korrys.com', 'http://www.cityofhenderson.com/parks/parks/paseo_vista.php', 'http://www.revitaantiagingcenter.com/testimonials', '1592064176', None, 'http://www.santosfairview.com', None, 'http://www.switchinkitchens.com', 'http://www.littlecaesars.com', None, 'http://www.ellekayegroup.com', 'http://7eleven.ca/store-locator/33259', None, None, 'http://www.kitchengourmetaz.com', 'https://www.batteriesplus.com/store-locator/oh/northolmsted/batteries-plus-927?utm_source=yelp&utm_medium=local&storecode=927', 'https://holisticlakewood.com', 'http://www.forestnailsandspa.com', 'http://www.massagehealthcare.com', 'http://tiredoctors.com', 'http://lonespurcafe.com', 'https://www.camdenliving.com/charlotte-nc-apartments/camden-south-end', None, None, '1592064386', 'http://www.UnexpectedVenue.com', None, '1592064415', 'https://holidayinnlongueuil.com/?utm_source=yelp&utm_medium=referral', 'http://azdistilling.com/', 'http://www.bamaspgh.com', 'http://rtcsnv.com', None, 'https://ad.doubleclick.net/ddm/clk/300117429;127049113;q', 'http://www.raphaelsbeautyschool.com', 'http://liznailsrockyriver.com', 'https://www.anytimefitness.com/gyms/866/Oregon-WI-53575/?utm_source=yelp&utm_medium=local', 'http://www.bridgespreschool.com', 'http://www.genoapizza.com', 'http://essostations.com', 'http://www.completeautomotivefairview.com', 'http://www.santanoralsurgery.com', None, 'http://www.thewinkinowl.com', 'http://polishedsalons.com', 'https://magicalstarpreschool.com', 'https://www.cellularsales.com/stores/verizon-4764-s-higley-rd-gilbert-az-85297/', 'http://www.abracleaners.com', 'http://www.liveatthestetson.com', 'https://www.hilton.com/en/hotels/clebhes-embassy-suites-cleveland-beachwood/?SEO_id=YELP-ES-CLEBHES', None, 'http://zombieburlesqueshow.com/', 'https://stores.hallmark.com/nv/henderson/amys-hallmark-shop-henderson-nv-65414.html', None, None, 'http://toronto.shambhala.org/', 'https://onekickgym.com', 'http://www.nctphoenix.com', 'http://www.akirabacktoronto.com', 'https://wolfgangpuck.com/dining/lupo-by-wolfgang-puck-las-vegas/', None, 'http://www.laserenaheights.com', 'http://www.tropicalbreezefrozendrinks.com', 'https://www.choicehotels.com/north-carolina/charlotte/rodeway-inn-hotels/nc168/rates', 'http://www.bramaleatire.com', None, 'https://www.nevadainsuranceenrollment.com', None, 'https://www.goldencoastii.com', 'http://jardin-thai.com/', None, 'https://paulpaddalaw.com', 'http://vegashotwater.com', None, None, None, 'http://www.mooreauto.com', None, None, 'http://MGpatisserie.com', 'https://www.corebellawellness.com', 'http://www.heartcleaneats.com', 'http://www.hhovv.org/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.BetterThanYiaYias.com', '1592064927', 'https://www.sonoraquest.com/find-a-location/phoenix-by-appointment-only-tatum-shea/', 'http://www.jordanbowden.com?cmpid=D3ZF_BLM_0006', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://stores.jcrew.com/en/j-crew-yorkdale', 'http://www.frostgelato.com', 'http://www.dairykingsoutheuclid.com/', 'https://www.target.com/sl/willoughby/1112', 'https://www.target.com/sl/fitchburg/2106', 'http://www.excalibur.com', 'https://www.zippssportsgrills.com', 'http://theshoebox.com', None, 'http://miracleeyebrows.com/', 'http://www.biteandsip.ca', 'http://www.247acaz.com', 'http://michaelsgenuine.com', None, 'http://www.mtlebanonpubandpizza.com', None, 'http://www.ipowerweb.com', None, 'http://kidzpreschool.com/contact/mountainsedgeandsouthernhighlands', '1592065153', 'http://www.doughboyspizzawaunakee.com/', None, None, 'http://www.evildeadvegas.com', 'https://www.marriott.com/hotel-restaurants/phxdr-jw-marriott-phoenix-desert-ridge-resort-and-spa/stonegrill/5543174/home-page.mi', 'http://streetfoodapp.com/', 'https://atriumhealth.org/medical-services/childrens-services/levine-childrens-hospital', 'http://www.snowpalacecalgary.com', 'http://www.makemydoor.com', None, 'http://www.cjgenterprise.com', 'http://www.rodiworld.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.hottopic.com', 'http://www.gtavapes.com', 'https://www.fortmillderm.com', 'https://www.learningjungle.com/en-US/lone-mountain/', '1592065314', None, 'http://www.arizonafederal.org', None, 'http://www.holeeburger.com/', 'https://www.peterpiperpizza.com/locations/mesa-az/gilbert-baseline', None, 'http://onestopnutrition.com', 'http://www.thebloordalepantry.com/', 'http://www.playitagainsam.com', None, None, None, 'http://www.churchs.com', None, 'http://www.starbucks.com', None, 'http://www.muchoburrito.com', 'https://www.chezmatante.ca/fr', None, 'http://www.thebarndoorstore.com/', 'http://www.carrefourmultisports.com/', 'http://www.loicgourmet.ca', 'http://www.swedishautowerks.com', None, 'http://www.theroomaz.com', None, 'http://sushishop.com', 'http://www.kensingtonriversideinn.com', 'http://www.ghardytours.com', 'http://www.marmiteafricaine.ca/', 'http://www.rcsandbar.com', 'http://www.theaustralianaz.com', 'http://www.pctravelservice.com', '1592065589', 'https://www.global-restaurant.com', 'http://www.tfsgolf.com/', None, '1592065626', 'http://www.dunkindonuts.com', None, 'http://www.locksmithsolutionslv.com', None, 'http://www.victoriaballet.com/', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.dollartree.com/', 'http://www.perfectionistcleaningservices.co', 'http://parkerautotransport.com/', 'http://www.mrfallstree.com', 'http://premiumnailsandspa.com', 'http://www.teamtheraputix.ca/', 'http://www.wholegrainbreadco.com/', 'http://www.sweettoothfestival.com/', 'http://www.hendersonhyundai.com', 'https://www.camelbackcollision.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'http://www.pizzahut.com/', None, 'http://www.xpresslubecharlotte.com', None, None, None, 'http://www.momos.ca', 'http://www.brdiamondsuite.com', None, None, 'https://www.reliablerooteraz.com', 'http://www.pitaland.ca', 'http://www.ActionComicsandSports.com', 'http://www.davisbakery.net', 'http://www.riverstonetaverne.com/', 'http://www.FiveStarPM.com', 'http://www.mrmechanicofaz.com', None, 'http://www.foodlion.com', 'http://www.zombiemfg.com', None, 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://emergencyfamilymovers.com', 'https://useggrestaurant.com/', 'https://www.nationalsports.com/pages/store-pickering-ontario', 'http://airkewld.com', '1592066020', None, None, None, 'http://www.lacasadecristo.com', 'http://cfnsaz.com', None, 'http://macmillanorchards.com/', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTWS', 'http://www.momskoreanfood.com', 'http://www.azpops.com/', 'http://www.mamaspizzamatthews.com', 'https://www.bannerhealth.com/locations/glendale/banner-thunderbird-surgery-center', 'http://www.starbucks.ca', None, None, 'http://www.montroseautooutlet.com', 'http://kidneypuncher.com/', 'http://www.drnoorda.com/', 'https://candrtire.com', None, None, 'http://www.bradfordclinic.com', 'http://www.theepicure.ca', None, None, None, 'http://www.timhortons.com', None, None, 'http://www.abstractahairsalon.com', 'http://hungrybeecatering.com', 'http://livingatlavie.com', 'http://www.pittsburgh-home-inspections.com/', 'https://www.finks.com/birkdale-village', 'http://www.fearsconfections.com', '1592066435', 'http://www.crossfitvenividivici.com', '1592066459', None, 'http://herbologytours.com', 'http://www.lorays.com/home', None, 'http://www.ateraspas.com', None, 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', 'https://stores.joann.com/oh/hudson/171/', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=phxch&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'https://www.seaboardbrewing.com', None, 'http://www.lavenderoldlace.com', '1592066560', 'https://www.sleepcountry.ca', None, 'http://www.picknsave.com/StoreLocator.aspx', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://newserenityspa.com', 'http://www.pesticon.com', 'http://www.sushieye.com/', None, None, None, None, 'http://www.worldoftile.net/wordpress/locations/scottsdale/', None, None, 'https://fitnesstogether.com/plaza-midwood?utm_source=Yelp%20Web&utm_medium=Yelp%20Web&utm_campaign=Yelp%20Web', 'https://handy-howies-handyman-services.business.site', 'http://nataliesnailsalonlasvegas.com', 'http://fiveguys.com/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, None, None, 'http://extremepita.com', None, 'http://www.solaruniverse.com/vegas', 'http://www.securitysupplystore.ca', 'http://jackastors.com/location-map/34/', 'http://www.lakenormancottage.com', 'http://sunsetwater.net', 'http://www.loveyoubackboutique.com', 'http://www.coach.com', 'http://www.scottsdaleoralsurgery.com/', None, 'http://www.davidsonday.org', 'http://www.babypointlounge.com', 'http://www.aerushome.com', 'https://www.dtlvarts.com', '1592066878', None, None, 'https://www.uber.com', None, None, 'https://www.theskincentermd.com/cosmetic-plastic-surgery-shadyside-pittsburgh-pa', 'http://www.PrecisionWindowTint.com', None, 'http://www.juicecore.com/', 'http://locations.einsteinbros.com/az/scottsdale/6501-e-greenway-pkwy-bldg-5.html?utm_source=storelocator', 'http://jewelrycitylasvegas.com', 'http://heartlakeauto.net', 'http://www.mcclurecollision.com/', 'http://canyonmidwifery.com', None, None, 'http://www.superstore.ca', 'http://www.atlascinemas.net', 'http://www.fosterinn.com', 'http://5two3.com', None, 'http://www.girlsgolfofphoenix.org', 'http://www.asu.edu/news/forthemedia/asufacts/campuses.htm', 'http://igniteglassandgifts.com', 'http://www.fixsys.ca', 'http://www.skydivelasvegas.com', None, None, 'http://guildresto.com/', 'http://www.focusbenefits.com', 'http://smokespoutinerie.com', None, 'http://www.jcprinting.net', 'http://www.passautos.net', 'http://www.papagiuseppes.com/', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.salonbellarouge.com', 'https://my.clevelandclinic.org', 'http://www.littlecaesars.com/', 'http://www.graciebarra.com/ahwatukee-az', 'http://www.marahselegantbridal.com', None, 'http://albertaballet.com', None, 'http://www.eyebrows4us.com', None, 'https://familydentistryofharrisburg.com', '1592067261', 'http://lenasrotianddoubles.ca', None, None, 'http://www.aquasystems.ca/', '1592067298', 'http://www.limoluxusa.com/', None, 'https://stores.cartier.com/united-states/nv/las-vegas/3131-las-vegas-blvd-south', None, 'https://www.reliablecouriers.com/service-area/arizona/phoenix', 'http://www.theoperahousetoronto.com', 'http://www.pinkberry.com/stores/15324', 'http://facejuvenate.com', None, 'http://www.tooltimehandymanservices.com', 'http://www.concordcustomcleaners.com', None, None, 'http://www.iriefoodjoint.com/', 'http://www.laherradero.com', 'http://www.insuremedave.com?cmpid=ram6_blm_0006', None, 'https://www.caseys.com/general-store/wi-de-forest/602-w-north-st/1936?utm_campaign=website&utm_term=organic&utm_medium=referral&utm_source=yelp&utm_content=1936', None, 'https://www.services.gov.on.ca/services/mapLocations.do?action=m', 'http://www.illinipubcycle.com', 'http://www.automotivespecialtyservices.com', None, 'http://mcmanusandcampbellhair.com', 'http://www.lv-pm.com', 'http://www.brunswickvolkswagen.com', 'http://www.tempe.gov/museum', 'http://www.firstchoicedental.com/locations/east-madison-office', None, 'https://smp-ink.com', 'http://www.lilliasdressmaking.com', 'http://www.firstcareclinic.org', 'http://www.redrockcanyonlv.org/hikes-trails/first-creek-canyon', None, 'http://www.discount-drugmart.com', 'http://rumrunnervegas.com/', 'http://www.starbucks.com/', None, None, 'http://thebco.com', 'http://www.oldworldbrewery.com', None, None, None, 'https://www.mattressfirm.com/stores/az/scottsdale/mattress-stores-scottsdale-az-85260-2922.html', None, 'https://www.walmart.com/store/1380/las-vegas-nm/details', None, None, None, 'http://www.flashtelwireless.com', 'http://www.hornekia.com', None, 'http://www.yogurtology.com', None, 'http://www.iliosnoche.com', '1592067721', None, None, None, 'http://baycathospital.com/', 'http://www.sportinglife.ca/', 'http://www.montebellasalon.com', 'http://www.salvationarmyusa.org', 'http://www.crossfitmecklenburg.com', 'http://Jjsgrubbshacknliquor.com', 'http://10minuteoilchangers.business.site', 'http://www.pizzacafe.ca', 'https://www.theneckandbackclinics.com/locations/southwest-las-vegas', None, None, 'http://nextgenelectrical.com', None, None, '1592067863', None, 'http://www.clarkcountynv.gov/Depts/parks/Pages/charlie-frias-park.aspx', None, None, 'http://www.dunkindonuts.com', 'http://www.shopnofrills.ca', 'http://santemedical.ca/', None, 'http://3rdphazebodyoil.net', 'http://www.mogowestlake.com/', 'https://www.23twelveluxe.com', 'http://painting.vegas', 'https://locations.rallys.com/az/tempe/1410-west-university', 'http://www.swisschalet.com', 'http://www.rfadezbarberspa.com', None, 'http://www.bluedogtraining.com', 'http://www.brueggers.com/', 'https://www.fitnessworks.com/locations/dobson-rd-chandler-blvd', '1592068059', 'http://www.freskamediterraneangrill.com/', 'https://www.choicehotels.com/pennsylvania/gibsonia/quality-inn-hotels/pa122/rates', None, None, None, 'http://www.coyoacangrill.com', 'http://www.dobsonspringsapartments.com', None, 'https://sites.google.com/site/brightcleantollesonlaundromat/', None, 'http://www.ihg.com/candlewood/hotels/us/en/tempe/phxbr/hoteldetail', 'http://www.guerlain.com', None, 'https://www.usps.com/', 'http://www.acelebritylimousine.com', 'http://www.laserspecialists.net', 'http://vegasstronglocksmithlv.com', None, None, 'http://www.centremecanix.com', 'http://www.schmitzdoor.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.fourturnberryplace.com/', None, None, 'http://www.lassendas.com', 'http://www.UnitedBloodServicesAZ.org', 'http://www.wildburger.ca', 'https://www.pizzadivinoaz.com', None, 'http://www.chicagojoesrestaurant.com', 'http://flopatio.com/', 'http://www.undrcard.com', 'https://www.cherrylash.com', 'http://restaurants.quiznos.ca/on/mississauga/CLARKSonCROSSING-L5J2Y4', 'http://www.kitcabinets.com', None, 'http://www.nevadaozone.com/', 'http://www.arizonaturnergroup.com', 'http://samwanna.com/', 'https://www.phxfray.com', 'http://www.azdonutco.com/', 'http://www.mtnroadcycles.com', 'http://www.martinisandmagicshow.com', 'http://www.ghhlasvegas.com', None, 'http://www.tradeinautobrokers.com', 'http://www.enterprisecarsales.com/location/39R2/Enterprise_Car_Sales_Bedford?mcid=iyp:277&CUR=yelp', 'https://local.biglots.com/az/tempe/4604?zcp=pd_local_yelp', None, 'https://tonysgaragelv.com', None, 'http://www.papajohns.com', None, 'http://www.searshomeapplianceshowroom.com/locations/phoenix-az', None, None, None, 'http://www.hivehealinghouse.com', 'http://americansprinklerlandscape.com', 'http://www.ckdesignslv.com', 'http://www.lasvegasoralsurgery.com', 'https://www.signaturestyle.com/locations/on/markham/first-choice-haircutters-51352.html', None, 'http://poopertrooperslv.com', None, 'https://www.charlottebraces.com/davidson-office-location', 'http://www.josephiarussi.com', 'http://www.yankeecandle.com', None, 'https://www.369bugs.com', None, None, None, None, '1592068718', 'http://www.frysfood.com/', None, None, 'https://www.lasvegassedation.com', 'https://vitospizzaglendale.com', 'https://www.amazinglashstudio.com/studios/az/phoenix/phoenix-ahwatukee', 'https://www.azpulm.com', '1592068798', 'http://www.cedarbraemall.ca', None, 'http://megansframing.com/', None, 'http://www.summitapartmenthomes.com', 'http://www.vegasgarageco.com', 'http://www.terroni.com/bar-centrale/', 'https://www.windsorstore.com/blogs/store-locator/nv-henderson-henderson-galleria-at-sunset', None, 'http://www.snaponoptics.com', None, 'http://rockinsul.com', 'http://www.thescottsdaleresort.com/restaurants/palm_court/', 'http://www.salsablancagrill.com', 'http://www.acupuncturevegas.com', 'http://www.blvdfoodcourt.com', 'http://www.drwiner.com/', None, None, 'https://lasvegasbankruptcylawyer.co', 'http://www.celebritytanning.com', '1592069006', 'http://beststripclublasvegas.com', 'http://www.hometastingroom.ca', 'http://www.clubredrocks.com/', 'http://greaterthancoffee.com', 'http://www.caferio.com/', None, 'http://www.MountainsideAir.com', 'http://adrenalinerushslingshot.com', None, 'https://www.take5oilchange.com/locations/oh/southeuclid-140/', 'http://www.pizzahut.com/', 'http://www.micabeauty.com', 'https://www.zeppestavern.com', 'http://www.woodworkerssource.com', None, 'https://www.steammaxx.net', 'http://www.arizonaveterinaryoncology.com', 'http://newellfarmersmarket.com/', 'http://www.theheadquarters.ca', None, 'http://www.sunrisekidsdental.com/', 'http://www.azprecisionpet.com', 'https://store.401games.ca', 'http://www.meineke.com/locations/il', 'http://medpost.com/location/surprise-az', None, None, 'http://www.wickedpixiehair.com', 'http://www.poorlittlerichgirlresale.com', 'http://www.karenwrightins.com?cmpid=G2LN_BLM_0006', 'https://lesliescleaningservice.wordpress.com', 'http://www.sacredseed.com', 'http://fiveguys.com/', 'http://www.raginuptown.com/', 'http://www.meadowspediatrics.org', 'https://www.sprint.com/storefronts/bd/sprint-pittsburgh-pa-15235-fcs-102/?ecid=SEO:Yelp:2020_Q1:LastMile', None, 'https://www.wokwithmingchinese.com', 'http://mdcpgh.com/', None, 'http://www.moochieandco.com', 'http://www.coronalandscape.com', 'http://www.devourphoenix.com', None, 'http://www.vegasvacuumsewing.com', '1592069417', None, 'http://www.rossstores.com', None, 'http://www.abercrombie.com', 'https://www.homedepot.com/l/Tempe-K/AZ/Tempe/85283/489?cm_mmc=seo-yelp&', 'http://www.framezillapgh.com/', 'http://carguyscanada.ca', 'https://www.enterprise.com/en/car-rental/locations/us/al/huntsville-madison-55ha.html?mcid=iyp:8368400', None, None, 'https://www.fyhanimalhospital.org', 'http://burritozone.ca/', 'http://www.malayakitchen.com', None, 'https://www.choicehotels.com/CN478?mc=blypypaf', '1592069575', 'https://clearviewplumbing.ca', 'http://www.azvalleydental.com', 'http://www.hiddencoveapartments.com', 'http://platinumhealth.ca', 'http://www.rachellallen.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'https://www.jerseymikes.com/3141', 'http://www.rexall.ca/', None, 'http://www.seah.ca', None, 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', None, 'https://www.kohls.com/stores/oh/stow-331.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', None, None, None, None, 'http://www.starbucks.com/store/9334/', None, 'http://pamperedhair.com', 'http://www.31kitchen.com', 'http://www.acsmartialarts.com', None, 'http://www.innovativeeyecare.net', 'https://theresortatsummerlin.com/dining/casual-dining/market-place-buffet-las-vegas/', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.mzdds.com', 'http://www.jeanniesgrooming.com', 'http://www.mobilemassagebychristina.com', 'http://www.acsm-clinic.org', 'https://www.anytimefitness.com/gyms/4149/Champaign-IL-61820/?utm_source=yelp&utm_medium=local', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.jessicahair.ca', 'http://www.teamafterburn.com', None, '1592070253', None, 'https://www.beemasterlv.com', 'https://sierraspringsdental.com', None, 'https://www.alfaromeousaofhenderson.com/contact.htm', '1592070319', 'http://www.boutiquetalulah.com', None, None, 'http://www.spirithalloween.com', 'http://www.rountreeplantation.com', 'http://www.forever21.com', 'http://serviceexpertscleveland.com/', None, 'http://suncontrollandscapes.com/', 'https://locator.bmo.com/Default.aspx?t=bb&lang=en&sid=8803', 'https://locations.wendys.com/united-states/sc/fort-mill/1800-hwy-160-w.', 'http://www.elmayarestaurante.com', None, None, 'https://www.brightnow.com/dentist-near-me/surprise-dentist/40110', 'http://www.lasvegascc.com', 'http://www.landscapeguy.net', 'https://www.cloverleafsuites.com/charlotte/', 'http://www.ihg.com/holidayinnexpress/hotels/us/en/phoenix/phxun/hoteldetail', 'http://myInsightImaging.com/AZ', None, 'http://www.azfaccs.org', 'http://www.phoenixhairextensions.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://rodneygentry.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006430627392&ds_s_kwgid=58700000443429206&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.onearmor.com', 'http://www.opusglow.com', 'http://www.hurleybrokers.com', 'http://www.Anchoranvilcoffee.com', None, 'http://www.greatclips.com/', 'http://sahniendo.com', '1592070593', 'https://www.chevronwithtechron.com', 'https://www.rayspizzacavecreek.com', None, 'http://www.hotelblackfoot.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://wwww.outlawscavecreek.com', 'http://www.beunailsbeauty.com', 'http://www.maggiesdonuts.com', None, 'https://www.johnfloydpaintingllc.com', None, None, 'http://carstarexpress.ca/locations/toronto/', 'http://www.coyoteplumbingandrooter.com', 'http://rothrockdmd.com/', 'http://www.mcmurraystylingcenter.com', 'http://danmarpetresort.com', 'https://www.MedgausDentalCare.com', 'http://www.starbucks.com', None, 'http://www.vietnampalace.ca', None, None, 'http://advancedanklefoot.com', 'http://www.sscandycigar.com/', 'http://signaturewest.net', None, None, 'http://www.burritoboyz.ca', None, None, 'https://www.moonvalleynurseries.com/services/tree-service-nevada?utm_campaign=yelp&utm_source=yelp-nv&utm_medium=tree-care', 'http://www.majesticeyebrowthreading.com', 'https://www.devitomd.com', None, 'https://www.harveys.ca', None, None, 'http://sofiasbraids.com/', None, 'https://www.aderraapts.com', 'http://goodwillsp.org/shop/retail-stores/second-editions', None, 'https://www.mattressfirm.com/stores/az/phoenix/mattress-stores-phoenix-az-85032-7927.html', 'http://www.azdmvaz.com/', 'http://www.TheMovementDanceExperience.com', 'http://www.hurstbakery.com/', 'http://www.sacktimemattress.com', 'http://www.bedbathandbeyond.com', 'http://www.shell.us', 'http://www.tambellinisbridgeville.com', 'https://electriciansmesaaz.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700007898397760&ds_s_kwgid=58700000649767852&ds_e_adid=%7Bcreative%7D&ds_url_v=2&cmpid=ADV_PG_%5B*KeywordID*%5D', 'http://www.redkingkong.com', 'http://www.bestbuy.com', None, 'http://eatnewchina.com', None, None, None, 'http://www.lvpremierpt.com', 'http://www.osteoklinika.com', 'http://koreangrillhouse.com/yonge-bloor-location/', 'https://www.providencedental.com', 'http://www.cabana-restaurant.com', None, 'http://www.dfwfurniture.com', None, 'http://www.impbaseline.com', 'https://www.walgreens.com/locator/walgreens-2324+w+war+memorial+dr-peoria-il-61614/id=6408', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.rumbi.com', 'https://arbatrestaurant.com', None, None, '1592071168', 'http://www.marshallretailgroup.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.firehousesubs.com/locations/oh/mayfield-heights', None, 'https://www.calldunrite.com', 'http://www.childrenslearningadventure.com/', 'http://www.bankofthewest.com', 'http://www.deweyscoffee.com', 'https://mercado-negro-tapas-restaurant.business.site', 'http://dethaicuisine.com', None, None, '1592071267', 'http://locations.harristeeter.com/nc/charlotte/205/', '1592071283', 'http://www.starbucks.com/store/8167/', 'http://www.amhomeservices.ca/', 'http://www.marbleslab.ca', 'http://castlecoffeelasvegas.myrestaurantpage.website', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://bikesharetoronto.com', 'http://storelocator.pepboys.com/pepboys/stores/chandler/chandler/00735', 'http://Www.makeupbynikkip.com', None, None, 'http://www.sevenhillsdentalcenter.com', 'http://www.stclairtanningspa.com', 'http://www.ontimevegas.com', None, None, 'http://www.lasvegasdiningtours.com/', None, 'http://www.airconditioningarizona.com/', 'http://www.spayaz.com/locations/mesa-az/', 'http://www.crossfitvenividivici.com', None, None, 'http://www.oakasushihouse.com', None, None, 'http://southeastlocksmith.com/', 'http://www.arizonacharliesdecatur.com/Food-Drink/Charlies-Market-Buffet', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://atechautocenter.com/', 'https://ad.doubleclick.net/ddm/clk/434184450;236814625;f', '1592071537', None, 'http://www.bonterrafarmmarket.com', None, 'http://solobace.com/', 'https://www.popeyes.com', 'http://holidayhoundhouse.com', 'http://zebreoptique.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', None, 'https://www.ediblearrangements.ca/stores/250-7th-Ave-SW-Calgary-AB-T2P-0W6', 'http://www.kaypacha.ca', None, 'http://whasn.com', 'http://www.winners.ca', 'http://www.elsantocantina.com/', 'http://www.thehomeshopnv.com/', 'https://stores.maccosmetics.com/us/oh/westlake/262-crocker-park-blvd', 'http://www.valueplace.com', 'https://stores.jcpenney.com/pa/pittsburgh/clothing-stores-pittsburgh-pa-2263.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2263', 'http://blackchickenwinecellar.com/', 'http://www.matthewsastrology.com', 'http://www.corrados.ca', 'http://www.apple.com/fashionshow', None, 'http://www.perfectprincesscut.com/', None, 'http://www.kouski.com', None, '1592071798', 'http://www.patdees.com/', 'https://order.subway.com/Default.aspx', 'http://fiveguys.com/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTVF', 'http://smartypaws.com', '1592071848', None, 'http://reflexologypedicure.blogspot.com/', 'https://www.lhshealth.com/cedarwood-plaza/', None, 'http://www.scottssharpening.com', 'http://www.starbucks.com/store/11425/', 'http://gratifyinggrains.com', 'http://dreamconnections.com', '1592071927', None, 'http://www.actionazcomputers.com', 'http://www.sushixtra.com', 'http://www.pinevillecomputers.com', 'https://corksncrafts.com', 'http://www.pictureshowent.com/home-mesa/', None, 'https://locations.whataburger.com/az/scottsdale/2955-n-hayden-rd.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', None, 'http://www.simplebistro.com', 'http://www.jimmysbackyardbbq.com', None, None, 'http://dentistrylasvegasnv.com', 'http://fishsandwich.ca/', 'http://yoamotacos.com/woodbridge-canada/', 'https://locations.theupsstore.com/pa/pittsburgh/4885-mc-knight-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.valentinos.ca', 'https://computerrepairdoctor.com/locations/cleveland/', None, 'http://www.sugarmarmalade.com/', 'http://www.winners.ca', 'http://www.originalchimneys.com/', 'https://www.hellotech.com/us/nc/mecklenburg/charlotte', None, None, 'http://www.champaigntruetires.com', 'http://www.hokkaidoseafoodsushi.com', None, 'http://www.innerstrengthchiro.com', None, None, None, None, 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2fnv%2flas-vegas%2fmidtown&sisearchengine=1524&siproduct=BEMDT_Bus', '1592072228', 'http://www.lettysonshamrock.com', None, None, 'https://www.wyndhamhotels.com/hotel/29495?tel=18882935571&iata=00093785&cid=fe:bh:20161215:yl:pp:hawus:29495', '1592072279', 'http://charlestonantiquemall.com/', 'http://apple.ca/retail/dix30', 'http://majerles.com/goodyear/', 'http://bebosmacshack.com', None, 'http://pamperohio.com/about.php', 'http://www.baystreetvideo.com/', 'http://www.bistro2182.com', 'http://staples.ca', None, 'http://www.uhhospitals.org/locations/uh-st-john-medical-center/st-john-medical-center-emergency-room', 'https://store.vioc.com/oh/brunswick/3675-center-rd-44212-060023', None, None, 'http://www.unionhillscc.com/', 'http://brighteyespa.ca', 'http://www.cosmictreats.ca', '1592072432', 'http://stardustvapes.org', None, 'http://www.nancyscheese.com', 'http://local.fedex.com/nc/concord/SRWA/', None, 'http://www.ososkatepark.com', 'http://www.alligatorpartyrental.com/', 'https://www.photobooths-charlottenc.com', None, 'http://jovanilinens.com', 'http://www.torontopearson.com/en/parking/#%23', 'http://mrgreek.com', 'http://www.thaihana99.com', 'http://www.FlawlessBeautiAndNailBar.com', None, None, 'http://www.cashamerica.com/SUPERPAWN-stores/AZ/PHOENIX/Pho18', 'http://www.holidayinn.com/hotels/us/en/toronto/yyzct/hoteldetail', None, None, 'http://vibrantcare.com', None, 'http://www.planetfitness.com/gyms/mississauga-dundas-st-on-1431?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'http://www.perfumes4u.com', 'http://www.fitness19.com', '1592072690', 'http://www.brisams.com/', None, 'http://www.dmelv.com', 'http://www.picea997.com', 'http://www.les3maria.com', 'http://www.jazz28.com', 'http://www.petland.ca/store-locator', None, 'http://www.tcccollision.com', 'http://www.advantaclean.com/las-vegas-nv', None, 'http://ccshvac.net', 'https://longevitymedical.com', None, 'https://tottoriallergy.com', 'http://richsautomotive.net', None, None, 'http://tasty-n-healthy.com/', 'http://www.reesors.ca/', 'http://www.tacoshuichoaz.com', 'https://www.azcasona.net', 'http://www.diamondtaxi.ca/', 'http://www.noblewindowcleaning.com', 'https://www.holysheetsusa.com', None, 'https://livepalmvillas.com', 'http://thelodgeatgrandtetonlasvegas2.cafesplanet.com', 'https://www.autumnparkcharlotte.com', 'https://www.hubbardswim.com', 'http://www.poolsnbeyond.com', 'http://www.littlerascalsrescue.com/', 'http://cityfreshpastapgh.com', 'http://www.primeroofingaz.com', 'http://www.lasvegasendodontics.com', None, None, 'http://uspalasvegas.com', 'http://stingraysushi.com/', None, None, None, 'http://www.pelicanssnoballs.com/', 'http://lakewoodmusicacademy.com', 'http://www.snvrha.org/index.htm', 'http://eastvalleysewnvac.com', 'http://www.daysinn.com/hotels/hotel-overview?wid=ps:addppc_yelp&tel=18003291073&reg=appc-_-ylPROPP-_-00405-_-diWES&hotel_id=00405&cid=whg_di_yelp', None, 'http://sushiave.net', None, 'http://www.silvercityrestaurant.ca', 'https://www.dontdrivedirty.com/locationsandpricing/?id=904', 'http://pages.wynnlasvegas.com/showstoppers', 'https://bluelakesassistedliving.com', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://www.facetofacefotographie.com', 'http://locations.harristeeter.com/nc/concord/202/', 'http://www.crownbuilders.com', 'http://www.mississaugahonda.com', 'https://www.goodfeet.com/charlotte', 'http://doorclosingsystems.com/', '1592073208', 'http://www.expressautospot.com', 'http://www.chestnutresidence.utoronto.ca/', 'http://www.naturalmeats.org', None, 'https://www.pizzaepazzi.ca', None, None, 'https://saenz-cleaning-llc-house-cleaning-service.business.site', 'https://einsteinplumbing.com/las-vegas-nv', '1592073287', 'http://www.thegreatinflatablerace.com/las-vegas', 'http://phenixsalonsuites.com/locations-detail/?id=94', 'http://www.houndhuddle.com', 'http://www.littlecaesars.com', None, '1592073354', None, 'http://www.stripdistrictmeats.com/', None, None, 'http://www.fearlesskittyrescue.org', None, 'http://www.rollinpizzapies.com', 'http://nsbank.com/', 'http://locator.carolinas.aaa.com/locations/pineville/', None, 'http://www.fortefamilypractice.com', 'http://www.arbys.com/', None, 'http://www.beatitudeschurch.org', None, None, 'https://www.alaskaair.com', 'http://www.discounttire.com/dtcs/makeAppointmentForStore.do?sc=NVL-12&utm_source=Yelp&utm_medium=iyp&utm_campaign=YelpIYPSA', None, 'http://www.parisoptique.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7784&localechange=1', None, 'http://thebreakawaybarandgrill.com/', None, 'https://www.riteaid.com/store-details?storeNumber=11467', None, 'http://storelocator.staples.ca/stores/fr_CA/QC/Saint-Laurent/21', 'https://www.supercuts.com/locations/sc/rock-hill/manchester-village-haircuts-82206.html', 'http://www.nacvegas.com', None, 'http://www.peoriashippingservice.com', 'http://www.bravaboutique.ca', 'http://www.saffronlasvegas.com/', '1592073756', None, None, 'http://gammajeansinhomedogboarding.com', 'http://www.eternitynailsspa.com', 'http://www.foodymart.com/', 'http://www.vogue-salon-spa.com', None, None, 'http://freshco.com/stores/bloor-dundas', 'http://www.tiltedgrill.com', 'http://www.northpointeyestudio.com', 'http://www.rightbuyautosales.com', 'https://www.jiffylube.com/locations/az/tempe/1665', 'https://www.choicehotels.com/wisconsin/madison/comfort-inn-hotels/wi415/rates', 'http://www.theinsidecoup.com', 'http://www.healingroots.center', 'http://www.lululemon.com/toronto/yorkdale?cid=yelp', None, 'http://tiffanynailsandspa.ca', None, 'http://www.ivoryparade.com', 'http://shehadys.com', 'http://www.torontonorthmitsubishi.ca', 'https://www.jiffylube.com/locations/nc/cornelius/3148', 'http://www.bridalboutiqueofaz.com', None, 'http://www.portofsubs.com/', None, 'https://yorkvilles.ca', 'http://www.atmospheresalon.com/', None, 'http://www.concordtavern.com', 'http://tyndallfurniture.com', 'http://www.las-vegas-locksmith.us/', 'http://www.saharamedicalinstitute.com', 'http://3vintagechicks.com/', 'http://www.edandmarks.com', 'http://www.eatoooweebbq.com', None, 'http://www.cbdefa.com', 'http://www.kuhars.com', 'https://www.mattressfirm.com/stores/nc/charlotte/mattress-stores-charlotte-nc-28277-5684.html', None, None, 'http://www.lalalunaspa.com', 'http://www.titansgym.com/index.php?Itemid=47&view=article&id=52&option=com_content', 'http://www.quiznos.com', 'http://www.sunpenang.com', 'http://www.stevenvance.com', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', '1592074181', 'http://makerealestateeasy.com', 'https://koliequestrian.com', 'http://www.goldmedalgym.com/chandler', None, 'http://www.freckaplumbing.com', 'http://www.mamaginaspizzeria.com', 'http://www.hotwire-electric.com', '1592074242', None, None, 'https://www.littledealer.com/pages/location%20phoenix', None, 'http://www.cleanandamazing.com', None, 'http://somagrill.com', 'http://www.xtremeperformance.info/', 'https://www.discounttire.com/store/nv/henderson/s/1300?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.gabesstores.com', 'http://5-starair.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://arthurmurray.com/locations/las-vegas-west-studio', None, 'http://www.winebeercigars.com', 'https://www.dairyqueen.com/us-en/locator/Detail/2398', 'http://www.glutenzerobakery.com/', None, 'http://www.cowboyciao.com', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', 'http://www.rebel-auto.com/', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=443', 'http://salsaritas.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.shoptieoneon.com/about-us.html', 'http://remachines.com', 'http://queencityrides.com', 'http://www.mazajloungecalgary.com', 'http://hahnsurvival.com', 'http://www.charmingcharlie.com/', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'https://www.starbucks.ca', None, '1592074521', '1592074530', 'http://www.scooterinvasion.com', 'http://www.zenewicznotary.com', 'http://www.onyxtheatre.com', 'http://www.mirasnails.com', 'http://www.gostorageone.com/self_storage/Las_Vegas_NV/zip_89130/storageone_self_storage/10494', 'https://www.dahntahndonuts.com', 'http://thirdeyebodyart.com', None, None, 'http://www.cjaimnotary.com', 'https://www.smalv.com/OurCenters/HealthCareCenters/Nellis', 'http://www.sinteriordesign.com', 'https://mstarkeychiro.com', 'http://www.provocateurimages.ca/', 'http://www.newwavemarket.com', 'http://www.dentistrybydesignchampaign.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.scratchkitchenclt.com', None, 'http://www.harlemrestaurant.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://classicchinesecuisine.com', 'http://www.thepreeners.com', None, 'http://www.organicmarketplacenc.com', 'https://www.officedepot.com/storelocator/nv/las-vegas/office-depot-6761/', None, None, 'http://www.surprisespringtraining.com', None, 'http://www.pickeringtoyota.com', None, 'http://www.bonniesprings.com/', 'http://www.divasalonspa.com/', 'http://wi.madison.charmingcharlie.com/fashion_accessories_madison_wi_124.html', None, 'http://roseandcrown.com/', None, 'http://www.buffalochipsaloon.com', 'http://rainbowcinemas.ca', 'http://www.grandchinesecuisine.com', 'http://www.azcommercialproperties.info/', None, 'https://bumpandroll.com', 'http://www.springmeadowliving.com', None, 'http://www.brakeshopaz.com', 'https://www.singyourstyle.com', 'http://lajollaexpress.net', '1592074921', None, 'http://calladams.com/', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=10538&localechange=1', None, 'http://www.bulwarkpestcontrol.com', None, None, None, 'https://yourfeetfixer.com/locations/chandler/', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', None, None, 'http://www.sofashack.com', 'http://mcneelyfamilydentistry.com', 'http://www.ludexauto.com', None, 'https://www.benjerry.com/gastonia', 'http://www.timhortons.com', 'http://raffin.ca', None, None, 'http://www.freshss.ca', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006435132512&ds_s_kwgid=58700000444952194&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.goodspeedperformance.com', 'http://www.ritzcarlton.com/en/Properties/Toronto/Dining/DEQ_Lounge/Default.htm', 'http://www.thesycamoreatscottsdale.com/', 'http://www.cobsbread.com/local-bakery/kingsland-calgary', None, 'https://fratellosdeliohio.com', 'https://www.wyndhamhotels.com/hotel/11185?tel=18007606483&iata=00093785&cid=fe:tl:20170523:yl:pp:tlus:11185', None, 'http://www.desertsparkle.com', None, 'http://allcityrefrigeration.com/', 'http://www.ipl-laserhairremoval.com', None, 'http://www.monicals.com/locations/monicals-pizza-of-tolono/', '1592075253', 'https://mercedes-benz-thornhill.ca', 'https://www.simonmed.com/locations/all/simonmed_imaging___summerlin', None, 'http://www.watericemesa.com', 'http://www.swisschalet.com', None, None, 'http://acehotel.com/pittsburgh', 'http://www.restauranttranscanada.ca', None, '1592075354', 'https://www.batteriesplus.com/store-locator/az/surprise/batteries-plus-616?utm_source=yelp&utm_medium=local&storecode=616', 'http://www.pioneersand.com', 'http://www.discounttire.com/', 'http://www.jonesoptical.com', 'http://www.illsecondthatonline.com', 'https://dealer.sprint.com/experts-choice', 'http://www.veneciagastonia.com', 'https://www.greatwolf.com/concord/dining-shopping/dining/loose-moose-cottage', 'https://www.scottsdale5thapts.com', 'http://www.shanghaipalacerestaurant.ca/', None, 'http://anytimefitness.com/en-us/clubs/582', None, '1592075489', 'http://lakecityair.com', 'http://www.level20lounge.com', 'http://www.vetteculture.net', 'http://chambersphx.com/', None, None, 'http://www.jimmythegreekgroup.ca', 'http://www.element-dayspa.com/', 'http://www.shopbop.com', '1592075568', 'http://www.the505e.com/', 'http://icyroll20.com', 'http://www.verizonwireless.com/stores/arizona/surprise/surprise-319434/', 'http://www.blizzyogurt.com', None, 'http://www.mygnp.com', '1592075632', 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/etobicoke-(1).aspx', None, '1592075661', 'http://homefabricsonline.com', 'https://kayahempco.com', 'http://www.planetfitness.com/gyms/kannapolis-nc-1212?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', '1592075693', 'http://myarizonasmile.com', 'https://www.navyfederal.org/?cmpid=bn%7Cyelp%7Cevgrn%7Cbrn%7Cnull%7Cnull%7C01/13/2020%7Cml%7Cnull', 'http://www.knitandsip.com', 'http://www.carpetmdonline.com', 'http://www.slcrealty.com', None, 'http://www.gvdentalcenter.com', None, 'https://www.apple.com/ca/retail/yorkdale/', 'http://www.pizzapanorama.ca/index.html', None, None, None, None, 'https://easternarizonaexterminating.com', 'http://envoguestyle.com', None, None, 'http://www.greenvalleypres.com', 'https://www.petsuppliesplus.com/Store/OH/Middleburg-Heights/Middleburg-Heights/28?utm_source=Yelp&utm_medium=Store-Page%C3%8A', '1592075851', 'https://www.hermanheylflorist.com', 'http://arizonanationalinsurance.com', None, 'https://www.sunrisepreschools.com/locations/dysart-thomas/?utm_source=yelp&utm_campaign=online_listing_goodyear_287&utm_medium=referral&utm_term=business_url', 'http://neurocnv.com/', 'http://www.showmethatsmile.com', 'http://www.facesbylorri.com', 'http://www.qinaturalfood.com', 'http://www.longos.com/store/storedetails.aspx?store_no=10', 'https://spbarbershop.com', 'https://www.nofrills.ca/store-locator/Jerry%27s+No+Frill%27s+Mississauga/3101?storeId=3101', None, 'https://www.advantage.com/location/las-vegas-mccarran-intl-airport-las/?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_local', 'https://www.walgreens.com/locator/walgreens-133+w+8th+ave-homestead-pa-15120/id=9674', None, None, '1592076007', None, 'http://www.bikesaviours.org/', 'http://saucelv.com/', None, 'http://www.splendidchinamall.ca', 'http://www.libertytintsolutions.com', None, 'http://scottsdale.hyatt.com', 'https://www.aceofheartscpr.net/locations/ace-of-hearts-cpr-las-vegas', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'http://www.re-newcabinets.com/', 'http://www.lloydsrestaurant.ca', 'http://www.medmassage.com', None, 'http://www.familyfarmcreameries.com', 'http://www.bloomingexpressionsflowers.com/', 'https://www.valero.com', 'http://www.norwinbowl.com', 'http://www.smilestraight.com', 'http://www.sunvalleyscooters.com', 'http://www.paperjoy.com/', None, 'https://www.redclayciderworks.com', 'http://arkvegas.com/restaurants_village-streets.htm', None, None, 'http://www.martelsalon.com/', None, 'http://www.theunicornpub.com', None, 'http://www.superstarmovers.com', 'http://www.tempe.gov/parks/', 'https://shop.wirelesszone.com/ma/hudson/234-washington-street', 'http://www.phoenixcarpetrepair.com', None, None, 'http://www.fernandosmexicanrestaurant.ca', 'http://scaasports.com', 'http://www.deervalleyplumbing.com', 'http://www.nspeds.com', 'http://www.americanapparel.net', 'http://www.sahara.bhhsnv.com', 'http://www.nobutei.com/', 'http://www.marvelmasonry.com', '1592076409', 'http://store.bobbiesflowers.com/?srccode=yelp_track', None, 'http://www.cicis.com/locations/nv-las-vegas-9890-s-maryland-pkwy', 'https://www.dontdrivedirty.com/locationsandpricing/?id=907', None, 'http://www.dilisosmeats.com', None, 'http://thebacklotbar.com', 'https://palmbeachtan.com/locations/AZ/Scottsdale-North-Scottsdale-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'http://www.procarehospicenv.com', '1592076498', 'https://www.harborinnseafoodcharlotte.com', 'https://www.kohls.com/stores/pa/gibsonia-1271.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.nsbank.com/branch/?branch=durango_and_215_south_branch', None, None, None, None, '1592076576', 'http://www.paradisemedspa.com', None, None, 'http://www.torontolivings.com', 'https://www.usps.com', 'http://www.scottspro.net', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=976', 'https://www.epoxylasvegas.com', 'http://www.pappertdentistry.com/', 'http://www.amjcampbell.com', 'http://www.valleyendodontic.com', 'http://www.encorelasvegas.com/#/entertainment/sinatra_dance_with', 'https://www.target.com/sl/glendale/1806', 'https://www.ulta.com/stores/gilbert-az-354', 'http://habitburger.com', None, 'http://www.greatclips.com/salons/6225', 'http://www.heavenscookie.com/', 'http://www.coolcomfort.net', None, 'https://late-night.business.site', 'https://mydeluxecleaners.com', 'http://www.thaiexpress.ca/', 'http://brotherspizzaandwings.ca', 'http://www.thechefon2wheels.com', 'http://www.reedkrakoff.com', None, None, 'http://www.big5sportinggoods.com', 'http://www.onelovegrapplingarts.com', 'http://www.eatatjoeydeli.com', None, 'http://www.montgomeryross.ca/', 'http://intouchcoachingllc.com', 'http://www.grottoshakersquare.com', 'http://www.ddsdiscounts.com', 'http://martininailbar.com', 'http://www.wedjaz.com', 'http://www.kasecustom.com', 'http://amadioranch.com', None, 'http://www.dworksautotintanddetailing.com', 'http://www.toothhealer.com', 'http://www.chbaz.com', None, 'http://gameworldvegas.com/', 'http://hearingassociateslv.com', 'http://www.kildares.ca', 'http://www.tablewinemadison.com', 'http://oohlalash.ca', 'http://www.ezpawn.com', 'http://www.starbucks.com/store/9298/', 'http://www.gnc.com', 'http://conniesjewelrygalleryandclockshop.com/', None, 'http://www.sushikanda.com/laval.html', None, None, 'http://www.quilles440.com/index_files/Page455.htm', 'http://www.oreillyauto.com', 'http://www.maxandermas.com/locations/333038', 'http://www.abreedapartanimalhospital.com', 'http://www.harbsauto.com', 'http://www.imagepluslasvegas.com', None, None, 'http://www.karachikitchen.com/location/brampton', None, 'http://www.flikandcompany.com', 'http://Skingri-la.com', 'http://www.theperfectshadesalon.com', None, '1592077170', None, None, 'http://www.calgaryautoquest.ca', '1592077203', None, None, None, 'https://www.beautybrands.com/store-locator/ahwatukee.do', 'http://www.rochestersdining.com', None, 'http://www.riverset.com', 'http://www.alohacardiology.com', None, 'https://www.ttc.ca/Subway/Stations/Wellesley/station.jsp', 'http://www.restaurantmissitalia.com/fr', 'http://www.charliesbarkpark.com', 'http://www.heartcenterofnv.com', 'http://www.networkautomotive.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.thaidtogo.com', 'www.edelweissimports.com', 'http://www.mcnallypianomovers.com/', 'http://www.daybreaknewmarket.com', 'http://www.wealthsimple.com', None, 'http://algobertoslasvegas.onlunchroom.space', 'http://phoenixcarnival.com', 'http://cabanatanolympia.business.site', 'http://www.bayrischerhof.biz', 'http://challengeyourgame.com/', None, None, None, None, None, 'http://www.phtowers.com/', 'http://www.raniasgrill.com/', None, 'http://www.dibellas.com/club-bread?source=yelp', '1592078201', 'http://www.burritoboyz.ca', None, 'https://locations.jimmyjohns.com/oh/southeuclid/', 'http://rusanscharlotte.com', 'http://www.brooklinbakery.ca', 'http://dukepubs.ca/westminster', None, 'http://www.regmovies.com/Theatres/Theatre-Folder/Regal-Severance-Town-Center-Stadium-14-822?utm_medium=social+network&utm_source=yelp&utm_campaign=yelp+-+description&utm_term=Regal+Cinemas+Severance+Town+Center+14', 'http://www.longjohnsilvers.com/', None, 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', '1592078324', None, 'https://www.ahn.org/location-detail?name=wexford_Health_%21_Wellness_Pavilion', 'http://www.legendswarehouse.ca', None, 'http://www.gordonsjewelers.com', 'https://www.mukujapaneseramen.ca', 'http://www.kyreneinternalmedicine.com', 'https://www.presleyuptown.com', 'http://www.rapaczdental.com', 'http://www.ethicalaz.com/moquinosbodyandpaint', '1592078404', 'http://www.reesors.ca/', None, 'http://www.absorental.com', 'http://isthmustattoo.com', 'http://azhairdoctor.com', 'http://www.natalyapanchenkostudios.com', 'http://www.thrifttown.com/', 'http://www.lecharmeroses.com', None, 'https://www.northpointecle.com', None, None, 'http://robraymagic.com/', 'http://www.busybuggy.com/', 'https://www.lvhomeinspection.com', 'https://store.vioc.com/nv/las-vegas/9631-trailwood-dr-89134-HC0003', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.arsenal201.com', 'http://www.aplusnanniesinc.com', None, 'http://www.waypointvacation.ca', 'https://www.wastedgrain.com', 'http://www.analogcoffee.ca', 'http://www.chandlerneurologyandsleep.com', 'http://rockinrollssushi.com', None, 'http://www.ymcacharlotte.org', 'http://www.pohlenv.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZXR', '1592078668', 'http://www.myoworksvegas.com/', 'https://www.cottonlanecitrus.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.villagerapartments.com', None, None, None, 'https://shop.nordstrom.com/c/wedding-suite-locations-beachwood-place?utm_source=yelp&utm_medium=organic&utm_campaign=wedd&utm_content=11227&utm_channel=lcl_brand_p&sp_source=yelp&sp_campaign=wedd', 'http://vegascaralarm.com', 'http://www.lubestop.com/Locations/Solon', 'https://www.fatcatsfun.com/gilbert', 'http://www.pinnaclevistavilla.com/', 'http://hharizona.com', 'http://www.sinatralv.com', 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'http://www.mlsalonspa.com', 'http://www.xplozone.com', '1592078860', None, 'http://bodyworksplus.com', 'https://circlecentreforhealth.com', None, 'http://www.hyatt.com/gallery/torphannon/kosher.html', 'http://www.halalbiryanihouse.com', None, 'http://longoortho.com/', 'http://www.emeraldsuites.com', 'http://www.gophoit.com/index.htm', 'http://www.sherwin-williams.com/store-locator/paint-store/Charlotte/NC/2164', None, 'http://www.attentiontoautodetail.com', 'http://www.club120.ca', 'http://www.onereddoorhudson.com/', 'http://pittsburgh.pirates.mlb.com/pit/ballpark/pncpark-events/venues/brewing-hall/', None, 'http://www.sunburstsmokeshop.com', None, None, 'http://www.DrJoyceChang.com', 'http://www.adogsbestfriendlv.com', None, 'http://www.jumpforfun.com', 'http://www.gonsteadperformance.com/', 'http://www.sunkissedtanninglv.com', 'https://www.purebarre.com/location/brecksville-oh', None, 'https://www.moderntortilla.com', None, 'http://bagelnash.ca', None, 'http://www.elevationweightloss.com', 'http://www.homegoodstore.com', None, None, None, 'http://www.frenchconnection.com', 'https://thirteen55motorsports.com', None, 'http://www.biltmorelifestylesre.com', None, 'https://megafurnitureusa.com', None, 'http://brittneywinklerhair.com', 'https://www.noons.co', 'http://www.eurocarsdetail.com', None, 'http://www.nailbrite.ca', 'http://worldofbeer.com/Locations/Gilbert', 'http://smartbuyavenue.com', None, '1592079287', None, 'http://www.pawsnclawsvet.com', 'https://www.smartstyle.com/en-us/locations/nv/las-vegas/located-inside-walmart-3473-haircuts-3334.html', 'http://www.christownspectrum.com', 'http://www.rebarn.ca', 'http://www.champps.com/', None, 'http://www.thepavilionsattalkingstick.com', 'http://www.merriperry.com', 'http://www.willowsdesign.com', None, None, None, None, None, 'http://www.dollartree.com', 'http://labambaburritos.com/', None, 'https://locations.teavana.com/us/az/scottsdale/7014-east-camelback-rd.html', 'http://whiskyattic.com/', 'http://apexendolv.com', 'https://locations.dennys.ca/AB/CALGARY/248179', 'http://www.alphadrone.com', 'http://sushibarkim.com/index.php', 'https://adamsplacerestaurant.wordpress.com', None, 'http://camelbacktailoringandalterations.com', 'http://www.firedupbbq.com', 'https://calgarycanine.com/auburn-bay/', None, 'http://www.oneshotinstallation.com', 'http://donutconnection.com/', 'http://www.goodfaithcasting.com', 'https://lvccld.org', None, 'https://www.sdi.edu', 'http://www.rslcs.org', 'http://www.coinlesslaundry.com/alma-school.html', None, 'http://www.oggiristorante.net/', 'https://www.ph216.com', 'http://www.shopnsavefood.com', None, 'http://www.manchuwok.com/', 'http://billskupa.com', 'http://www.cellphonerepaircomputerrepairlasvegas.com/', 'https://www.smartstyle.com/en-us/locations/nv/north-las-vegas/located-inside-walmart-2592-haircuts-3346.html', 'http://www.zernichlaw.com', 'http://www.greatdjmusic.com', '1592079719', 'https://www.redshoeslv.com', 'http://www.brighton.com', 'http://www.breadandsalt.ca', 'http://www.verizonwireless.com/stores/ohio/westlake/westlake-202670/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://zeroissuebeer.com', 'https://www.corepoweryoga.com/free-week?utm_source=yelp&utm_medium=cta&utm_campaign=chandler-yelp-free-week', 'http://www.ljkusina.com', 'https://www.kungfutea.com', None, None, 'https://www.discounttire.com/store/az/scottsdale/s/1284?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://desertridgemusicacademy.com', 'https://www.popeyes.com', 'http://www.martislounge.com', None, None, 'http://lylesjewelryandcoin.com', '1592079878', None, 'http://www.luckyhuelv.com', None, 'http://www.colonyroofing.com', None, None, 'http://www.mentorsportsbar.com', 'https://www.randrrefrigeration.com', 'http://kaizenautocare.com/body-shop-phoenix-az/', 'http://www.dsw.com', None, None, 'https://www.pristinemobiledetailaz.com', 'http://frysfood.com', None, 'http://www.hotdeallio.com', 'http://locations.michaels.com/NC/GASTONIA/5006/', 'http://www.enochturnerschoolhouse.ca/', 'http://AutoNationSubaruScottsdale.com', None, None, 'https://www.mezu.ca', None, 'http://racquetclubscottsdaleranch.com', 'https://www.stbank.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://kitcarson.snappages.com/', None, 'http://manchuwok.com', 'http://affinityplumbingaz.com', 'http://www.pizzadepot.ca/locationDetails/21', 'http://www.keratinspecialist.com', None, 'http://www.sincityvapor.com/', 'https://www.thebrick.com/pages/store-mississauga', 'http://www.villasatgreenvalleyapts.com', 'http://sojoramenlasvegas.taverndesigner.site', '1592080235', None, 'http://www.timhortons.com/', 'http://www.ahappydogwash.com', None, 'http://www.lids.com', '1592080274', 'http://www.johnrobertsspa.com', 'https://northscottsdale.tapoutfitness.com', 'https://1transmission.wixsite.com', 'http://www.momdocwfw.com/mercy-gilbert', 'https://my.clevelandclinic.org/locations/directions/225-brunswick-family-health-center', 'http://charmeck.org/city/charlotte/Airport/Parking/Pages/CellPhoneLot.aspx', 'http://idealdentistryaz.com/', 'http://www.DNDC.ca', 'http://www.crescentphx.com/', None, 'http://www.regency.edu/campus/tinley-park-illinois.aspx', None, None, None, 'http://www.coffeetime.com', None, 'http://www.connectionsarizona.com', 'https://mollymaid.com/west-glendale-avondale', 'https://www.baskinrobbins.com', 'http://www.maidbrigade.com/az/phoenix', 'http://azcyclery.com/', 'https://stores.guitarcenter.com/las-vegas-lessons?source=4GOA5AJBB', 'https://rvonthego.com/arizona/paradise-rv-resort/?utm_campaign=Yelp_Directory_Listing&utm_medium=directory&utm_source=Yelp', 'http://www.ranchomanana.com/', 'http://www.stratospherehotel.com', 'http://michaeldaily.com', 'http://www.winnerstraining.com', None, 'http://monkpatisserie.ca', 'http://www.mypopcornheaven.com', 'http://www.mc3salon.com/', 'http://www.andersonentertainment.co', 'http://biggunenterprisesllc.com/', None, 'http://www.glenatmesa.com', 'https://www.hilton.com/en/hotels/msnbjhx-hampton-suites-madison-downtown/?SEO_id=YELP-HP-MSNBJHX', 'http://concordncattorney.net', 'http://www.curetondentistry.com', 'http://eastsidemarios.com', None, None, 'https://www.theflowercart.org', 'http://www.serenevegas.com', 'http://www.outback.com/locations/az/surprise', None, None, 'https://haroldstudio.com', None, 'http://alsshoerepair.com', 'https://www.garciadiamondsusa.com', None, None, 'http://bodyworkscenter.net/', 'http://www.barbershopjack.com', None, None, 'http://www.charlotterestore.org', 'http://www.chopstixhenderson.com', 'http://www.billysroadhouse.com', 'http://www.fieldclub.org/', None, 'http://www.xcitemobilegamingcharlotte.com', 'http://www.dentalhygienegroup.ca', 'https://mbveuro.com', 'http://oaksautotruckservice.com/', 'http://www.securitytitle.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/nj/colonia-2471.html?mcid=iyp:8368400', None, None, 'http://www.thecortinaapartments.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044282967372&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.gnc.com', 'http://www.nexuscarelv.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.agramgardencentre.ca', 'http://www.petvethospitals.ca/morningside-pet-hospital/', 'http://www.restomeridiana.com', None, 'http://www.face2toe.com', None, 'http://teslamotors.com', None, 'http://www.lvsmiles.com', 'http://www.starbucks.com', None, 'http://www.theweavescene.com/', None, 'http://athoriagames.com', 'http://america-sunshine-maintenance.com', 'http://www.arizonatmjpain.com', 'http://www.redrocklasvegas.com/dining/cabo.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=RR&utm_content=RR-PROPERTIES&utm_campaign=RR-YELP', 'http://www.christysnursery.com', None, 'http://www.insuranceofvegas.com/?cmpid=wj16_blm_0006', None, '1592081138', 'http://www.discount-drugmart.com', 'http://www.arrowmedaz.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://www.Rooneys.Market', 'http://www.vitalant.org', '1592081204', 'http://rsecatering.com/', 'http://rebozos.ca', 'https://www.bbbuggy.com', 'http://www.villageinnrestaurants.com', 'http://www.craigroadcarwash.com', 'http://freshsifoods.com', 'http://www.gogibson.com', 'http://www.fatburger.com/home/', 'http://www.pitapit.com/', 'http://www.aumaubree.com/', 'http://oxygenrestaurant.ca', 'https://www.freshthyme.com/store/oh-westlake/', 'http://www.tinderboxcigars.com', 'http://www.brooksidelawnservice.com', 'https://www.truecocktailsbites.com', None, 'https://www.zaxbys.com/locations/nc/denver/7179-highway-73/', 'http://www.lovethreadingbar.com/', None, 'http://truearizonaliving.com', 'http://pigandduke.com/', 'http://ignite.fortis.edu/?BID=3038&VID=SR_CID-000045038666', 'http://www.moes.com', '1592081418', 'http://www.esourceparts.ca', 'http://www.qualityinn.com/hotel-madison-wisconsin-WI089?source=pmfyelp&pmf=yelp', 'http://www.satisfiedfrog.com', None, 'http://www.fceglobal.com/', 'https://www.lifetimefitness.com/en/programs-and-events/lifestyle/lifespa/arizona/goodyear-palm-valley-lifespa-hair-skin-nail-spa-facilities.html', 'http://phoenixmoversunlimitedinc.com', 'https://curaleaf.com/stores/pl/curaleaf-az-central-85040/', 'http://www.arbys.com/', 'http://www.towcompanymesa.com', 'http://thepurrrfecttouch.com', 'https://dutchbros.com/?utm_source=las-vegas&utm_medium=yelp&utm_campaign=website_las-vegas', 'http://www.linatranstudio.com', None, 'http://www.terryalixsalon.com', 'http://www.cupcrazed.com', 'http://shymcgrath.com', 'http://asiannoodletogo.com', None, '1592084427', None, 'http://www.themandrakeclt.com', None, 'http://www.AppleOne.com', 'http://www.originalhoagieshop.com/', None, 'http://www.modernrevivalevents.com/', None, 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, None, 'http://calibercollision.com/locate-a-caliber-collision-center/las-vegas-downtown/', 'http://barksbubblesgrooming.com/', 'http://www.customalterationsbyanne.com', 'http://www.kingcoleducks.com', 'http://climb-cleveland.com', None, 'http://my.clevelandclinic.org/staff_directory/staff_display.aspx?doctorid=4363', 'https://www.americancampus.com/student-apartments/az/tempe/vista-del-sol', 'https://www.perfectpalmssalon.com', 'http://www.finaticsaquarium.com', 'http://www.jrsweets.ca', '1592084616', 'http://www.acuraeast.com', 'http://www.grillcity.com/nevada/bbq-grill/', None, None, 'http://www.cowlickhairsalon.com', None, None, 'http://www.magnoliaroom.com', 'https://www.wyndhamhotels.com/hotel/52962?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52962', 'http://www.pro-edgecutleryaz.com', 'http://www.elitedestinations.net', 'http://www.fourstarsushi.ca', 'http://clickserve.dartsearch.net/link/click?lid=43700006430791267&ds_s_kwgid=58700000444977937&ds_url_v=2', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.attractagency.com', 'http://www.valleyrentabox.com', 'http://Www.garbarinos.com', 'https://www.swoon.cc', None, None, 'https://www.lakenormannailsbar.com', 'http://www.studiofontana.ca', 'http://www.e-zrentacar.com/locations/las-vegas-airport', None, 'https://hpautorepair.com', None, None, 'http://www.pizzahut.com/', 'http://thesman.com/las-vegas-meadows', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://affordableweddingminister.com', 'https://www.drnnadi.com', None, None, 'https://www.autozone.com/locations/pa/wilkinsburg/208-penn-ave.html', None, None, None, None, 'https://stores.dickssportinggoods.com/nv/las-vegas/1266/', None, 'http://www.themadisonapartmentliving.com', None, None, 'http://www.entsoa.com', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', 'http://www.harborcrestapts.com', None, 'http://www.bottega.ca/index.php', 'https://badaxethrowing.com/axe-throwing-vaughan', 'http://www.rockincleveland.com', 'http://www.enatethiopianrestaurant.com', '1592085010', None, 'http://www.thecamptc.com', 'http://portsalonandspa.com', 'http://www.tso.ca', '1592085055', '1592085064', None, 'http://www.jimboys.com', None, None, 'http://workshopcalgary.com', None, None, None, 'http://charandarestaurante.com/', 'http://www.pattersonroofingco.com', 'http://www.armaantasteofindia.com', None, 'http://www.citywidetowing.com', 'https://www.officedepot.com/storelocator/nv/las-vegas/office-depot-3351/', 'https://www.hilton.com/en/hotels/lasethx-hampton-suites-las-vegas-airport/?SEO_id=YELP-HP-LASETHX', 'http://www.achristmasstoryhouse.com', 'http://www.cannabition.com', None, '1592085206', 'https://www.sleepcountry.ca', 'http://www.tenfeettall.ca/', 'http://myezroofsolution.com', 'http://mellomotive.com', 'http://www.sciullispizza.com', 'https://resurrectioncarpetcleaning.com', 'https://www.dodsonbros.com/location/charlotte-south/', 'http://www.russellchiro.net/', None, 'https://www.goldsgym.com/chandler-az/', 'http://fortyrodroadhouse.com', 'http://www.hendricktoyotaconcord.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, 'https://petmedic.vet/hospitals/providence-pet-hospital/', 'http://www.thewholeplate.ca', 'http://www.richardsautoclinic.com/', None, 'http://www.melonhead.ca', 'http://www.harryrosen.com/store/Vaughan%20Mills', 'http://www.rpspasta.com/', 'http://www.themaidcrusade.com', 'https://www.pintocashforgold.ca', 'http://www.willemandjools.com', 'http://www.abrazohealth.com/facilities/ArizonaHeartHospital/home.aspx', None, 'http://www.surefireinstitute.com', 'https://www.choicehotels.com/pennsylvania/coraopolis/comfort-suites-hotels/pa327/rates', 'http://www.kidszonedurham.ca', None, None, 'http://www.kennywood.com', 'http://www.avriorx.com', 'http://www.marcelwaffles.com', 'http://crumblcookies.com', 'http://www.thaiexpress.ca/', 'http://www.justincrain.com?cmpid=RV5O_BLM_0006', 'http://bestwestern.com', None, 'https://www.peoriapines.com', None, 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.aquarelarestaurant.com/Dominican_Restaurant_Toronto_-_Aquarela/Welcome.html', 'http://www.desertbloomskincare.com', 'https://locations.cibc.com/on/toronto/03902?q=Toronto%2C+ON+M4K+1P7&loc=M4K+1P7%2C+ON', 'http://masterwerks.com/', None, 'http://robertostacoshop.com', None, None, None, 'http://www.weprintvegas.com', 'https://angel-dentalcare.com', 'https://www.urbanoutfitters.com/en-ca/stores/downtown-toronto', 'https://www.repairngo.com', 'http://www.oasisislandvegas.com', 'http://www.airconditioningrepairinphoenix.com/', 'http://www.paloverdedentistry.com', 'https://www.benjerry.com/davidson', 'https://www.anytimefitness.com/gyms/690/Fitchburg-WI-53719/?utm_source=yelp&utm_medium=local', None, None, 'http://southwestcajunfest.com', 'http://locations.scootaround.com/lasvegas', 'https://www.tidedrycleanersaz.com/locations/e-frank-lloyd-wright-blvd', None, 'https://www.fragranceoutlet.com/pages/fragrance-outlet-tanger-outlets-westgate-114', 'https://www.exxon.com/en/gas-station/tempe-az-tholdings2165-321058', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.mygym.com/henderson', 'http://www.southwestbikes.com', 'http://www.thepittstopbbq.com/', 'https://www.missionmontessori.com', 'http://www.chandlerjewishpreschool.com', None, 'http://www.chinaonepgh.com', None, 'http://www.pandaexpress.com/', 'http://www.davisvilleparkvets.com', 'https://lawnlove.com/charlotte-lawn-care', None, 'http://www.stitchit.com', None, 'http://kidscuckoosnest.com', None, '1592085834', None, 'http://www.coolsummercamp.ca', 'http://www.phxskin.com/', 'http://www.magnetitecanada.com', None, None, None, None, 'http://www.diamondbackcleaners.com', None, 'http://asurology.com', 'http://www.maxstudio.com', 'http://thefloatfactor.com', 'http://www.hairdistrict.ca', 'http://www.republicservices.com/', None, 'https://order.iamaflowerchild.com', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', None, 'https://secondcup.com', None, 'http://www.altour.com', 'https://www.gogeisel.com', 'http://www.sincitytint.com', 'http://www.landeseye.com', 'http://www.superstore.ca', None, 'http://www.academyofnails.net', 'http://www.stevenkretchmer.com/', None, '1592086116', None, 'http://www.cineplex.com/Theatre/cineplex-cinemas-scarborough', 'http://www.crowbarlasvegas.com', 'http://azwindowreplacement.com', 'https://www.jrsmulchsales.com', 'http://www.mywellnessplace.com/', '1592086195', None, 'http://www.summerwindsnursery.com', 'http://palace.awardspace.com/', None, None, 'http://www.danieljsalons.com', 'http://www.southhillsortho.com', None, None, 'http://www.blackcatespressobar.com', None, 'http://jtsconcrete.com', 'http://www.magnolialanelv.com', 'http://www.bergstrommadisonchevrolet.com', 'http://www.thevillagedentalcenter.com', None, 'http://www.walterstation.beer', None, 'https://www.officedepot.com/storelocator/nc/kannapolis/officemax-6480/', 'http://www.aztacoshack.com', None, None, None, 'http://www.tranestudio.com/', 'http://www.gabroy.com', 'http://www.doughnc.com', 'http://www.maxmcqs.com/', 'http://www.popsphotoandtrophy.com', 'http://www.jaysatthelake.com', 'http://summerlinbarbershop.com/summerlinbarbershop/', 'http://www.destihl.com/', None, 'http://www.lasvegasskinspa.com/', 'http://www.northhillstoyota.com/', 'http://www.drlomboydc.com', None, None, None, None, 'https://www.hungryhowies.com/store/hungry-howies-00829?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00829&utm_content=Website_Link', None, None, None, None, 'https://www.kyrene.org/apr', 'http://www.hoopershealth.com/store-information/store-information-brampton/', 'http://www.cosmoprofbeauty.com', 'https://www.unlvmedicine.org/clinic/internal-medicine-0', 'http://www.hairyt.com', '1592086614', 'https://mettlercenter.com', 'http://stlouiswings.com', 'https://bhmanagement.com/communities/az/phoenix/cielo-apartments-1794/', 'http://woodchesterautoglass.com', 'http://castironwaffles.com', 'http://www.caronpartners.com', 'http://www.debruinchiropractic.com', 'http://proshops.bowlersmart.com/locations/nevada/bowlersmart-henderson-pro-shop-inside-strike-zone-sunset-station', None, 'http://www.windowprollc.com', 'http://www.mildreds.biz/', 'http://theupsstore.ca/45', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Phoenix/AZ/8160', 'http://www.hennaflorist.ca', 'http://murphyslaw.pub', 'http://website-3132959076228282333140-nailsalon.business.site', None, 'http://cksbbqlv.com', 'http://thewhitebrickkitchen.com/', 'http://www.teamonsiteconcrete.com', 'http://www.eighty8family.com', 'http://www.romaninconcrete.com', 'http://www.safelite.com', 'http://madison-west.certapro.com/?source=Yelp', 'http://sassygurl.ca', 'https://www.azspiritualmedium.com', 'http://yourbuybacks.com', None, None, None, None, None, None, None, 'http://www.bhfcfinancial.com', 'http://www.angelblessingslv.com/', 'http://www.stonebowlkorean.com', 'http://www.liveattheurban.com', None, '1592086982', 'http://www.bigotires.com/regions/Nevada', None, 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', None, None, None, 'http://phoenix-9thandbell.titleboxingclub.com/', 'http://www.thevineyard.ca/', 'https://www.anytimefitness.com/gyms/2195/Richmond-Hill-ON-L4E-3L6/?utm_source=yelp&utm_medium=local', 'http://www.mygreek2go.ca', 'http://stephenfolsondds.com', None, None, 'http://keyspleaselocksmith.com', None, 'https://www.woodbridgeinteriors.com', 'http://www.powernailspa.com/', 'https://www.homedepot.com/l/N-Scottsdale/AZ/Scottsdale/85260/472?cm_mmc=seo-yelp&', 'http://www.hair2000.ca', None, None, 'http://www.bestchickenwings.com/', 'http://www.faziopizza.com', 'http://www.sprint.com', None, 'http://shusalon.com/', 'https://www.lawkm.com', 'http://www.thetrteam.com/?agent=mahalalel-leli', None, 'http://5starpdrllc.com', None, None, 'http://www.bennettmedical.com', None, 'http://www.sulwer.com', 'http://www.ryerson.ca', 'https://locations.theupsstore.com/wi/fitchburg/2935-s-fish-hatchery-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.modernsalonandspa.com', 'https://scottsdaledaycare.com', 'http://www.venetian.com/casino/race-and-sports-book.html', 'http://www.waterway.com', 'https://parteeputt.com', 'http://www.vapelandphx.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.preferredpublicrelations.com', 'http://www.flashlightfactory.net', '1592087399', None, None, None, 'http://cloisterhoney.com/', 'https://horizoneye.com', 'https://www.autozone.com/locations/nv/las-vegas/1021-w-owens.html', 'http://www.audiprestigeddo.com', None, 'http://www.hpb.com/041', 'https://stores.joann.com/nv/henderson/2015/', '1592087498', 'http://www.buldak.ca', 'https://www.westwindintegratedhealth.com', 'http://www.rtosullivans.com/', 'http://www.thechefandyou.com', 'https://locations.checkers.com/nv/north-las-vegas/2720-n.-las-vegas-blvd/?utm_source=Yelp', None, 'http://magnoliapetwc.com', None, 'http://subway.com/', 'http://gotrmc.org', 'http://www.quiktrip.com', 'http://capitalacupuncture.janeapp.com', None, 'http://www.firehousegrillingco.com', 'http://www.threesheetsdtlv.com', None, None, 'http://www.cccnevada.com/doctor/josette-e-spotts-md-facs/', 'http://www.greatclips.com/', 'http://www.kokobellibagel.com', 'http://jpsushi.ca', 'http://protechautogroup.com', None, None, None, 'http://www.teresaspizza.com/richfield', None, None, '1592087749', None, 'http://www.donsbees.com', 'http://LugariPet.com', 'http://popeyeschicken.ca', 'https://arizona-firearms.com', 'http://www.paramountbutchershop.com/', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Phoenix-AZ-85027/858046/', 'https://www.hertz.com/rentacar/location/unitedstates/northcarolina/charlotte/CLTT12', 'https://www.greendrop.com/calgary', None, None, None, 'http://www.bluelinegrille.com', 'http://www.shakeys.ca', None, 'https://www.lattaplantation.org', 'https://www.cybermax-pc-phone.repair', 'http://www.latan.com', None, None, 'http://web.archive.org/web/20071110183536/www.city.cleveland.oh.us/around_town/city_highlights/landmarks/freestamp.html', 'https://www.jerseymikes.com/3128', None, 'http://www.thecopperpalmsapartments.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.colorglolasvegas.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://www.thepotatobarn.com', 'https://northernsmokes.com', 'http://www.pandmpizzainc.com', 'http://www.brakemasters.com', 'http://www.towercitycenter.com/', 'http://www.crazymocha.com', 'http://www.bloordovercourtappliances.com', None, None, 'http://www.carmellaspizzagrill.net', 'http://www.thebluefoodtruck.com', 'http://www.kumon.com/PHOENIX-DESERT-RIDGE', 'http://www.creativeleather.com/', None, 'http://www.lecreuset.com/stores/charlotte-premium-outlets-charlotte-nc', 'http://www.ahwatukeechurch.com', 'https://stores.advanceautoparts.com/pa/carnegie/1011-washington-ave', 'https://charlotte-bjj.com', 'https://www.galleriavillage-apts.com', None, None, 'http://www.theairteamlv.com', 'http://www.northcentralsportsbar.com', None, 'https://epdpestcontrol.com', None, '1592091673', None, 'http://www.innerdivafitness.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.waltsbbq.com', 'http://www.lpoecharlotte.com', None, 'https://maps.rbcroyalbank.com/locator/searchResults.php?t=6702', None, None, None, 'https://www.campbowwow.com/cuyahoga-falls/', None, 'http://www.asba.com', 'http://cccwindowcleaning.com', 'http://metrodiner.com', 'http://www.sunnynutrition.com', None, 'https://www.jamescheese.ca', 'http://mattas.com', None, 'http://www.autoglassnow.com/phoenix', 'http://www.auntieleechampaign.com/', None, 'http://evolvedancecenter.com', 'http://www.luigismadison.com/', None, 'https://www.noodlebarphx.com', 'https://elitefloorandfurniturecleaning.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.yogibar.ca/', 'http://www.centerforbehavioralhealth.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://ineffablecaphe.com', 'http://www.thecitycafeaz.com/', 'http://www.floresfamilydental.com', 'https://www.thejoint.com/north-carolina/mint-hill/mint-hill-12029', 'http://sweetrepublic.com', 'http://www.thecaptainsboil.com?utm_source=Yelp&utm_medium=Click&utm_campaign=ON_5313Yonge&utm_content=mainlink', 'http://www.blueheel.ca/', 'http://sweetiefry.com', 'http://www.aecne.com/', 'http://www.carriepatriciastudios.com', None, 'http://www.platosclosetstrongsville.com', None, None, 'http://thegreatgreekgrill.com', None, None, 'http://www.wilderfood.ca', '1592092073', None, 'http://trunightclublasvegas.com', 'http://www.pouroliveoil.com', None, 'http://www.massagebar.com/pit.htm', 'https://penrose.edu/student-salon-and-spa', 'http://www.foodbasics.ca', 'http://www.t-mobile.com', 'http://www.azmulticare.com', None, 'http://www.yourbrowbar.com', 'https://www.advanceamerica.net', 'http://www.blossomdayspa.com', 'http://www.anticaosteria.ca/', 'http://mtholly.us/park_and_facility.php?3', None, '1592092204', 'http://www.ezpawn.com', None, 'http://wigwamcreekdental.com', None, None, 'http://enchantedcastle.info/', 'http://rosenailbarsummerlin.com', 'http://www.greatlakesbeer.com', 'http://habibizcafe.com', 'http://www.villagediscount.com/', 'http://www.tocayopgh.com', 'http://www.shuku2salon.ca', None, 'https://www.britishairways.com', None, 'http://www.elmolinocafe.com/', 'http://www.vedasfitness.com', 'https://www.infuzelv.com', None, 'http://www.winghouseandsportsbar.com/', 'http://www.eyewearatthehamptons.com', None, 'http://www.funkutzkidshairsalon.com/', '1592092400', 'http://expresssmogandmotorworks.com', None, 'https://www.affordablegaragedoor.biz', 'https://www.nhsteelecreekfamilymedicine.org', 'http://www.dhl.ca', 'http://www.azcrittergetter.com', 'http://www.smokesweinerie.com/', 'http://www.pizzapizza.ca/', 'http://www.southlandvisioncare.com', None, None, None, None, None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/1/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://iflyelite.com', 'http://www.crossfits3.com', None, 'https://www.argentaapts.com', 'http://www.guitaror.ca', 'http://hotyogaoncrowfoot.com/', 'http://Localocksmiths.com', 'https://www.tillys.com/store?StoreID=0044', 'http://www.woodbineanimal.ca', 'http://www.shilohcommunity.com', None, 'http://www.cochranvwnorth.com', None, None, 'http://www.fulloutperformance.com', 'http://caveatemptorlv.com/', '1592092620', 'http://www.bigalsbargrill.ca', 'http://www.theglostudio.com/', 'http://www.thematka.com/', 'http://thetkto.com/', 'http://www.pestcontrolguaranteed.com', None, 'http://belmontdrivein.20megsfree.com', 'http://marcellospastagrill.com/', 'http://www.roysrestaurant.com', '1592092690', 'http://aldi.us/index_ENU_HTML.htm', None, 'http://petersenicecream.com', None, None, None, None, 'https://www.hilton.com/en/hotels/phxclhw-homewood-suites-phoenix-chandler-fashion-center/?SEO_id=YELP-HW-PHXCLHW', None, 'http://www.apria.com', 'http://www.bk.com', None, 'https://www.caesars.com/caesars-palace/things-to-do/cleopatras-barge?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=CocktailCabaret&utm_content=entertainment', 'http://www.keshaschairlv.com', None, 'http://www.thesweetspotcleveland.com', None, 'http://www.3030southwater.com', 'http://www.presotea.ca', None, 'https://www.biscuitsrestaurants.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.sunscreensbymark.com', '1592092906', None, None, 'https://www.ahnenchiropractic.com', None, 'http://www.sincerelyyogurt.com', 'http://vipbilliards.ca', 'http://www.roosterscharlotte.com/', None, 'http://www.autosood.com/fr/', 'https://www.capriottis.com', 'http://www.starbucks.com/store/11135/', None, 'http://www.americanapparel.net', 'http://www.searsucker.com/scottsdale/', 'http://www.gogofresco.org', 'http://www.frankstowngardens.com/?srccode=yelp_track', None, 'https://local.fedex.com/az/scottsdale/office-2256/', 'http://www.sheahomes.com/newhomes/charlotte', 'http://www.integratedmha.com', 'http://arcadia.redemptionaz.com/', None, 'http://www.elevationoncentral.com', 'http://www.gilbertappliancestore.com', 'http://www.firelightbarn.com', None, 'http://www.southcharlotte.youvegotmaids.com', 'http://valleyprocessservice.com', None, None, None, 'http://www.foreverdiamondsjewelers.com', 'http://newmanprop.com', 'http://www.platosclosetlyndhurst.com', 'http://drappliance.business.site', 'http://99only.com/store/Las-Vegas---Beltway/', 'http://www.azbreastfedbabies.com', 'http://www.mobileaxs.ca', 'http://firstpictureframe.ca', None, None, None, 'http://advanceddermatologynevada.com/about-us/jan-fu-md-phd-faad/', None, 'http://www.sccarcenter.com', 'https://www.choicehotels.com/nevada/boulder-city/quality-inn-hotels/nv062/rates', None, 'http://www.animalkennelcare.com', 'http://www.mccandlesscrossing.com/', None, 'http://www.kmart.com/stores/pennsylvania/pittsburgh/3529.html', 'http://www.blomedry.com', 'http://www.steve-n-kids.com', 'http://www.brickandbarleyaz.com', None, 'http://www.residoor.com', None, 'http://www.massageheights.com/matthews-festival', 'https://pranaivtherapy.com', None, 'https://dillonmcdonald.vipmtginc.com/apply/', '1592093393', None, 'http://www.spamadison.com', None, None, 'http://www.drsibel.com', 'http://www.MODERNMILK.com', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', None, 'http://www.tacotimecanada.com/locations/alberta/calgary/deerfoot-meadows', 'http://www.apple.com/retail/northlakemall/', 'http://www.starbucks.com/store/10759/', 'http://www.sharkys.com', 'http://www.riggsroadvets.com/', 'http://www.head2toesmassage.com', None, 'https://www.ikea.com/us/en/stores/las-vegas/', 'http://Geeksquad.com', None, 'http://www.nevadaheadache.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.omwest.com', '1592093574', None, 'https://nolmsted.onyxhealthclub.com/contact/', None, 'http://westgatenailsspaglendale.com', 'http://www.stjosephphoenix.org', 'https://www.dickblick.com/stores/ohio/cleveland-heights/', None, 'https://www.familydentalcharlotte.com', 'http://www.swearlv.org', 'http://www.shawarmabox.ca', 'http://Www.summitpsychologicalservices.org', 'http://www.oldnavy.com/products/peoria-az-store-6364.jsp', 'http://www.myrosatis.com/store-details/Mesa%20Greenfield', 'http://www.mamarosespizza.com', None, None, 'http://www.underwrapslv.com', 'http://www.russellhendrix.com', 'http://www.wisconsinfencing.com', None, None, 'http://www.holatapasbar.com', None, 'http://www.autonationtoyotatempe.com/', 'http://www.shawarmaave.ca', None, 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, 'http://www.abcsforchildren.com', 'https://locations.sonicdrivein.com/az/tolleson/9552-west-van-buren-avenue.html', 'http://www.lackscleaning.com', 'https://www.psgdental.com/locations/precision-orthodontics-lyndhurst/', None, None, None, 'https://LimitlessGraphix.com', 'http://kachinapainting.com', None, 'http://www.fuchsiaspa.com', 'https://azfunandsun.com', '1592093870', 'http://www.deserttitle.com', None, 'http://www.trundlemanor.com', 'http://www.wrapsodygifts.com', None, 'http://tsujiri-global.com', 'http://www.sundevilbookstores.com', 'http://www.sophiespizza.ca', None, 'http://greenlifelawncare.net/', None, None, 'http://www.xoxolashes.com', 'https://www.freshcoatpainters.com/glendale-az', 'http://thesmokincue.com', None, 'http://www.centennialparkgolfcentre.com', 'https://hcpnv.com/clinic/la-canada-cardiology/', 'http://www.tanglesmadison.com', None, 'http://www.valleyartcenter.org', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.chatime.com', 'https://www.choicehotels.com/arizona/phoenix/econo-lodge-hotels/az191/rates', None, None, 'http://www.angrygorillamarketing.com', None, None, None, 'http://www.premierdentalal.com', 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', 'http://www.bunkerhillgolf.com/bar_and_grille/', 'http://advancedcleaningscottsdale.com', 'http://www.ckokickboxing.com/las-vegas.html', 'http://www.portcityclub.com/', 'https://locations.davidstea.com/on-markham-167', 'https://www.target.com/sl/streetsboro/2157', None, None, 'http://thebutlerdidit.info', 'http://www.rootcandles.com', 'http://mistertransmissionnewmarket.com', 'https://www.oxifresh.com/locations/az/paradise-valley-carpet-cleaning/?utm_source=yelp&utm_medium=social&promo_code=YP5000', 'http://www.lasvegaspropertyvaluation.com', None, 'http://www.mcknight-kitchen.com', 'http://www.aulddubliner.com/', 'http://www.cabanaondumont.com', 'http://www.lubie.ca/', 'http://www.seventattoostudio.com', None, 'http://www.goldwaterbank.com', 'http://yang39y.wix.com/xiangweixuan', '1592094322', None, '1592094333', 'https://www.johnsonlarsendental.com', 'http://www.mcadenvillemotors.net', 'https://locations.churchs.com/az-scottsdale-685', 'http://mauidogrocks.com', 'http://www.socialeatery.ca', 'http://www.newstylenailshenderson.com', 'http://eosfitness.com/location/centennial?utm_campaign=vegas-centennial&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', None, 'http://www.nicholaselectric.com', 'http://www.appetitebooks.ca/', 'http://www.futureshop.ca/', 'http://storelocator.pepboys.com/pepboys/stores/glendale/63rd_and_bell/00779', None, 'http://www.phoenix.invisiblefence.com', 'http://www.wilddogdigital.com', 'http://www.verizonwireless.com/stores/nevada/las-vegas/katie-203158/', 'https://www.davescosmicsubs.com', 'http://www.cocoshairstudio.com', 'https://www.target.com/sl/las-vegas-blue-diamond/2164', 'http://pjobrokerage.com', None, 'http://www.valleywidedoor.com', 'http://www.thaifootmassageaz.com', None, None, 'https://marketbrewingco.com', 'http://groutsmithcharlotte.com', 'http://www.bestfuneralservices.com', None, 'http://www.aactionmovers.com', 'http://www.mcsorleys.ca', None, 'http://www.camelviewpt.com', 'http://vaseklaw.com', None, 'http://www.shayacuisine.com', 'http://www.pizzapizza.ca', 'https://www.moesbarbershopaz.com', 'http://www.regencyheightsapartments.com', 'http://www.asiankitchencleveland.com', 'http://www.nationalspecialtypharmacy.com', 'https://www.spencediamonds.ca/location/vaughan-on/?utm_source=Yelp&utm_medium=Display', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', 'http://www.valleypaincenters.com', 'http://www.pipercleo.com', 'http://www.ashleysbeautylounge.com', 'http://mobiletecsmallengines.ca', 'http://www.zamrestaurant.com/', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', None, 'http://www.partybusesinvegas.com', 'https://www1.shoppersdrugmart.ca', 'https://www.etiquettesystems.com', None, 'http://www.hardrockhotel.com/las-vegas-restaurants/goose_island_pub', 'https://www.absolutedental.com/locations/las-vegas/2301-e-lake-mead/', 'http://uptowncheapskate.com/charlotte', 'http://www.dontortaco.com', 'http://www.spbcnc.org', 'http://www.seeingdoublecle.com', 'http://www.dogpolitan.com', 'http://www.bistrosirwilfrid.ca', 'http://crispycrust.ca', 'http://www.mcgoverns.biz', 'http://www.cadencehealthcentre.com', 'http://www.besolasvegas.com/', 'http://mayaclubaz.com', 'https://www.occphx.net', 'http://www.gamestop.com', 'http://Www.remosbistro.ca', 'https://www.petsmart.com/stores/us/az/phoenix-store0131.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.periospecs.com', None, None, 'http://www.azsingingcrepe.com/', 'http://www.andlerdental.com', 'http://bocalocaburritofactory.com', 'http://www.azbestgaragedoors.com', None, 'http://www.lazeezshawarma.com/', None, None, None, 'https://www.rightautoandtruck.com', None, 'http://www.cielostudios.ca', 'https://kirinbuffet.net', 'http://www.beatleshowvegas.com', 'http://www.metroicare.com/', None, 'https://www.bowdog.ca', None, None, 'http://www.greentreeprinting.com', 'http://www.vientianepalacerestaurant.com', 'http://jep-landscaping.com', 'http://www.germanbreadbakerylasvegas.com/', None, None, 'http://www.maxwellspine.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.greatclips.com/', '1592100552', None, None, 'http://www.drtomgreco.com', 'http://www.deerbrookefarm.com', None, None, None, 'https://americanaddictioncenters.org', 'http://www.marriott.com/cmpts', 'http://www.myspace.com/sweetsandbeats', 'https://locations.jackinthebox.com/us/az/scottsdale/20385-n-hayden-rd', 'http://www.budsayathaispalv.com', 'http://www.coderedplumbing.com', 'http://www.abcbartending.com/vegas/index.htm', 'http://www.starbucks.com', 'http://www.silversagebeef.com', None, 'http://lunchboxcafeaz.com', 'http://www.onedaypittsburgh.com', None, 'http://coolblew.com', None, None, 'http://www.oreilyauto.com', 'http://www.lvchamber.com', None, None, 'http://www.owloptometry.com', 'http://www.approvedaz.com', 'http://www.horizonlaservision.com/', None, 'http://zulmamassagetherapy.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.vapeandco.com', None, 'https://goo.gl/2UEpRZ', None, 'http://www.322PizzaBar.com', '1592100862', 'http://www.blackmountainbmx.com', None, 'http://www.dunkindonuts.com', '1592100900', None, 'http://www.crystalrivergems.com', 'http://swimmingpoolslasvegasnv.com', None, 'https://satruck.org', 'http://www.nickscalgary.com', None, None, 'http://www.caldensebakery.ca/', None, 'http://www.azsprinklerpros.com', None, None, None, 'http://www.oakridge-kennels.com', 'http://www.qdoba.com', 'http://www.arizonalodgingexperts.com/', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282947950&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.vegasconciergedoctor.com', None, 'http://www.teaspressa.com', 'http://mdrainlaw.com', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.dynastyirondoors.com', 'http://www.pineviewauto.com', 'https://www.extraspace.com/storage/facilities/us/ohio/kent/501645/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.crazymocha.com', 'https://www.royalautosales.ca', 'https://automotivediagnosticspecialties.com', 'http://www.greatescape-to.com', 'http://www.greatclips.com', None, 'https://rigatonys.com', 'http://www.sunrisemontessori.com', None, None, 'http://asavvyskincare.net', 'http://www.gabyetjules.com/', 'http://www.tcvintageaddiction.com', 'http://www.starbucks.com/store/9298/', 'http://www.CompleteLaserAZ.com', 'http://www.expressscreenprinting.com', None, None, 'http://www.tshirthell.com/', None, 'http://www.katkuphotography.com', 'http://www.greatclips.com', 'http://www.nutbrownschristmastrees.com', '1592101294', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'http://www.mrshawarmaairdrie.ca/', None, 'http://www.harborddentistry.com', 'http://porterhouseto.com/', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Pittsburgh-PA-15237/809064/', 'http://www.ihg.com/hotelindigo/hotels/us/en/scottsdale/phxin/hoteldetail', 'https://www.homedepot.ca/en/home.html?eid=LS_Google_7061', None, 'http://www.goldes.com', None, 'http://www.splitsville.ca/locations/woodbridge-bowling', '1592101389', None, 'https://www.target.com/sl/chandler-south/2747', 'http://www.worldscoutingmuseum.org', 'http://fuyaosupermarket.ca', None, 'http://www.scottsdaleaz.gov/parks/scottsdalemall', 'http://www.valleyinteriors.com', None, '1592101459', 'https://www.redradishcharlotte.com', None, 'http://www.matsudasushi.com/', None, 'http://www.starbucks.com/store/10759/', None, 'https://www.wellsfargo.com', 'http://www.stowglass.com', 'http://www.ramsey-auto.com/', 'http://mazzeolaw.com', 'https://www.tech1auto.com', '1592101541', 'https://www.suncountryheatingandcooling.com', None, 'http://www.taylorsflooringaz.com', 'http://www.asgnv.net/', 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', None, 'http://cpllabs.com/', 'http://www.dandelionretro.com/', 'http://www.freshkabob.com/', None, '1592101619', 'http://www.restorationhardware.com/', 'http://serenityspapeoria.com/', 'http://www.bannerhealth.com/locations/avondale/banner-physical-therapy-mcdowell-107th?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', None, 'http://www.phoenixcountryclub.com', 'http://www.krauterdds.com', None, 'http://sthielpilates.com', 'http://www.advanceddermatologylv.com/', 'http://www.UltraCleanExpress.com', 'http://www.littlecaesars.com', 'http://evansotg.com', 'http://www.pitabasket.com', None, 'https://www.ulta.com/stores/surprise-az-176', None, 'https://www.scaddabush.com/sherway/', 'http://www.carltonsharley.com', None, 'http://shadysidedetail.com/', 'https://www.hendersondentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://vbarbershop.com/locations/gilbert/', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85234/7110-in-gilbert/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-7110&utm_content=website-link&howheard=IYE', None, None, 'http://karsonskornbread.com', 'http://www.starwoodhotels.com/sheraton/property/dining/index.html?propertyID=205', 'http://www.pi-co.ca', 'http://www.itsbarmagic.com', None, 'http://www.painconsultantsofarizona.com', 'https://www.popeyes.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://harbour60.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.kidsacademyofcopley.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PITMC', None, 'http://www.marriott.com/hotel-restaurants/phxcb-jw-marriott-scottsdale-camelback-inn-resort-and-spa/blt-steak-scottsdale/125727/home-page.mi', 'http://www.mobilicity.ca', None, 'https://www.cricketwireless.com', 'https://www.ycsignsllc.com', 'http://www.fantasticfiredept.com/', 'http://www.busybodiesplayground.com', 'http://exquisitemobiledetailingllc.com', None, 'http://www.imperialflowershop.net/?srccode=yelp_track', 'http://www.yogaplustoronto.com', 'https://www.myessentia.ca/fr/magasins/laval/', 'https://torontovaporizer.ca', 'http://www.GurrBrothers.com', None, 'https://www.cleoms.com/meet-us/meet-the-doctor/dr-urban-picard/', None, 'http://thaipepperlv.com', 'http://www.orthoarizona.org', 'http://www.tirekingdom.com', None, None, 'http://www.barbsbridalboutique.com/', None, 'http://johnandsonsoysterhouse.com', 'http://www.allamericanlandscape.net/', None, 'http://www.kickerspizza.com', 'http://www.jlcolesalon.com/', 'http://obsessionbeautysalon.com/', 'http://www.allstateselfstorage.com/self-storage/bell-85032', 'http://www.risingphoenixllc.com', '1592102184', 'http://www.rasputinvodkabar.com', 'http://www.hkasiancuisine.com/', 'http://prioryfinepastries.com', 'http://alnolashoerepair.com', None, 'http://mvrwholesale.com/', 'http://www.rankinwomenscenter.com', 'http://www.curvyconsignments.com', 'http://www.krantzelectricinc.com/', 'http://www.gilcontool.net', 'http://www.themobilewebapps.com/repairwatchandjewelry', 'http://7eleven.ca/store-locator/33259', 'http://queencitylawn.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=2767&utm_content=bpas', None, None, None, None, 'http://www.hauntedpittsburghtours.com', 'http://www.pebooks.com/lv2/', 'http://www.kavicwinery.net/5701.html', 'http://www.waincapital.com', 'https://www.dentalsummerlin.com', 'http://slslasvegas.com/thebuffet', 'http://swensonelectric.com', None, 'http://www.westernexterminator.com/las-vegas', 'https://www.lebos.com', 'http://www.figarosbarbershop.com/', 'http://www.totallychiinc.com', 'http://www.fiddlersgreenpub.ca/', None, '1592102421', 'http://www.druglessdrs.com', 'http://www.learningrx.com/akron-bath', 'http://projectrefinedlife.com/group-private-yoga/', 'http://www.essenceairllc.com', 'http://www.amazingyoga.net', 'http://www.FatAngelosPizza.com', 'http://blinkeyewear.ca', None, 'http://www.bufords.kitchen/locations/downtown/', 'http://thenailspapgh.com/', 'http://lawanthaikitchen.com', None, 'http://harrisonautos.com', 'http://www.poppydenvegas.com/', 'http://www.reveregolf.com', 'http://clarkcountypoolandlawn.com', 'http://www.carpetsharkslv.com', 'https://www.summerlin.com/downtown-summerlin/overview.html', 'http://velvetlanecakes.com', 'http://www.cameostudio.com', 'http://1therapeuticmassage.wix.com/massage', 'http://www.muchoburrito.com', 'http://athleticmindedtraveler.com/browse-cities/toronto-on/university-of-toronto-athletic-centre', 'http://californiapools.com', None, 'http://www.apricotflowers.com', 'http://www.avon.com', None, 'http://www.MaderaPoint.com', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.mindfulwellnessaz.com', 'http://www.opalskinwax.com', 'http://www.sunkistpoolslv.com', None, 'http://www.greenroadpediatrics.net', 'http://www.room1six.com/', 'http://corktowndental.com', 'https://www.massageaddict.ca/Toronto-TheBeach', 'https://www.changingtimesdiaperco.com', 'http://www.zefiessmoothies.com', 'http://dynoplumbinglv.com', None, 'https://www.permenterchiropractic.com', 'http://scofieldrealty.com', None, None, 'https://stores.hallmark.com/nv/lasvegas/amys-hallmark-shop-lasvegas-nv-63960.html', None, 'http://www.globex2000.ca/fr', None, 'http://www.awrswheelrepair.com/pittsburgh', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Toronto-ON-M9M2R5/848075/', '1592102864', 'http://www.gnc.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.burritoboyz.ca/', 'https://ca.tokyosmoke.com/pages/queen-west', 'http://copperwillowsalon.com', 'http://www.stoughtonbuyandsell.com', 'https://integritydry.com', 'http://zero20kids.com/', None, 'http://walmart.com/', 'http://www.motel6.com', None, 'http://www.caldensebakery.ca', 'http://appliancewarehouse.com/', None, None, 'http://www.cafedejapon.com/', 'http://drshawnae.com', 'http://parrcabinet.com', 'https://www.towndentalgroup.com', 'http://www.theblindmannc.com', 'https://storelocations.ae.com/us/az/phoenix/4550-east-cactus-road.html', None, 'https://www.springspreserve.org/visitor-information/divine-cafe.html', 'http://www.solutionbuild.ca', 'http://www.northwestlimo.com', 'http://fairtradecoffeehouse.com/', 'http://www.starbucks.com/store/10759/', None, 'https://locations.wendys.com/canada/on/ajax/80-bayly-street-west', 'http://www.fredsheatandac.com/', '1592103130', 'http://newyork51pizzeria.com/', 'http://www.starbucks.com/store/14175/', 'http://www.radichisalon.com', 'https://encompasshealth.com/valleyofthesunrehab', 'http://www.fantasyautoinc.com', 'http://www.elitebusinessfilms.com', 'http://shop.pistolwhippedpastry.com', None, 'http://www.evanjstrong.com/', 'http://www.cbsquaredhairstudio.com', None, '1592103225', 'http://www.clevelandprintwear.com', None, 'http://www.jolantainteriors.com', None, None, None, None, 'http://www.pisausa.com', 'http://www.bashas.com/', 'http://www.playitagainsportscfalls.com', 'http://www.rvpaintrepair.com', 'http://www.janetkirkman.com/', 'http://www.ccvglass.com', 'https://www.massagespacharlotte.com', None, 'https://www.ritasfranchises.com/Wexford', 'http://bogartspet.com', 'https://www.jerseymikes.com/9003', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Tempe-AZ-85213/723082/', None, 'http://www.beyondconceptionmidwifery.com', 'https://www.24hourfitness.com/gyms/las-vegas-nv/rainbow-las-vegas-supersport', 'https://craftypots.studio', None, 'https://ad.doubleclick.net/ddm/clk/318369417;146857521;q?https://www.safelite.com/stores/Mesa?utm_source=yelp&utm_medium=list&utm_campaign=Addressblock&utm_content=85210_AZ', 'https://vspa-massagespa.business.site', 'https://winecollective.ca/highfield-store', 'http://www.thetoothwhisperer.com/index.html', 'https://opticas2020.business.site', None, None, 'https://drbeverlysmathisel.wixsite.com/drbeverlysmathisel', None, 'http://www.echosalonphoenix.com/index.html', 'http://www.guyspizzaco.com', None, 'http://www.dphairdesigns.com/', 'http://www.markmitsuphoenix.com', 'http://beegee-kitchen.com/', 'https://www.wm-columbuspark.com', 'http://www.infinitebeautysalon.com', None, 'http://www.sundevilauto.com/locations/az/mesa/east-mesa-power-26', 'http://www.flowersoftheworld.ca', 'http://patonthebackspa.com', 'http://pdrpizza.net', None, 'http://bankerinsulation.com', 'http://www.mainstreetcupcakes.com', None, 'http://www.veinitymd.com', 'http://mcfaddendalehardware.com', 'http://www.massagenirvana.com', 'http://www.timhortons.com', None, None, 'https://www.lush.ca/on/demandware.store/Sites-LushCA-Site/en_CA/Stores-Info?StoreID=129', 'http://www.acrepair4less.com', 'http://locations.jambajuice.com/ll/US/AZ/Scottsdale/15686-N_-Frank', 'http://www.timhortons.com/', None, 'http://www.GreaterPhoenixAreaRealEstate.com', 'http://xtremeairparks.com', 'https://www.steaknshake.com/locations/nv-las-vegas-las-vegas-boulevard-south', 'http://cambiedesign.com', 'https://ca-en.caudalie.com/boutique-caudalie-sherway-gardens-toronto', None, None, None, None, None, 'https://karachi-kabab-wala.business.site', 'http://www.azcellphones.com/', 'http://kjscurrybowl.com', None, 'https://grantmma.ca', 'http://phoenix-phx.worldairportguides.com/terminals.php', 'http://www.oldtimecandy.com', 'http://americanhomewater.com', 'http://www.footsolutions.com/summerlin', 'http://www.brownsshoes.com', None, None, 'http://eyecandispa.com', 'http://www.seanssalon.com', 'https://www.barlouie.com/locations/us/az/tempe/tempe-marketplace?utm_source=other&utm_medium=listings', 'http://www.bikramyoganphx.com/', 'http://www.nationalgolfacademy.ca', None, 'http://www.luxurymotorsports.us/used-luxury-cars-phoenix/', 'http://zcoilcf.zcoil.com/137/', None, 'http://www.fatbobpizza.com', 'http://www.swarovski.com/en-US/?utm_source=YELP&utm_medium=referral_managed&utm_campaign=YELP', 'http://www.west49.com', 'http://geigerfitness.net', 'http://Clearqualityautoglass.com', None, 'http://www.zenshinasianrestaurant.com', 'http://www.veginyyc.com', 'https://www.californiaclosets.com/locations/greater-phoenix/scottsdale-showroom/?CC5=32008&CC6=30593&utm_source=directory&utm_medium=local&utm_content=AZ166-M1-SR2', 'https://lulasewickley.com', 'http://www.fatbastardburrito.ca', 'http://www.wellsfargo.com', 'https://www.gordmans.com', 'http://www.chagrinfalls.net/', None, None, None, 'http://www.coconutclubbargrill.com', 'http://www.imaginedentistry.com', 'http://oldchicago.com/locations/champaign', 'https://www.interdent.com/gentle-dental/locations/az/mesa/1425-s-greenfield-rd-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.haysroofing.com/', 'https://www.integritycontentsservices.com', None, 'http://smilesourceonchagrin.com', 'http://etonhouse.ca', 'https://tsperformance.net', 'http://www.dressbarn.com', 'http://www.buildabear.com?sc_cid=ds:yelp:profile', 'https://locations.theupsstore.com/pa/harrisburg/4075-linglestown-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://greenwoodrentals.ca/', 'https://www.bikesourceonline.com/articles/bikesource-denver-pg502.htm', None, None, None, 'http://www.signaturehealthinc.com', 'https://www.snakesandlattes.com/location/tempe/', None, 'http://yourspacesalons.ca/tonyc', 'http://www.americanairappliance.com', None, None, 'http://www.theacvh.com', None, 'http://www.thisaint.ca', 'http://www.lasvegaswoodflooring.com/', 'https://www.insomniacookies.com/locations/store/1129', None, 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', 'http://shell.us', 'http://www.ghost-armor.com', 'http://www.thegunsmith.com/thegunsmith.html', 'http://treasureisland.com/restaurant/13/the-buffet-at-ti', None, None, 'https://www.rotorooter.com/murrysvillepa/', None, 'http://harrys-market.business.site', None, 'http://shop.hobbylobby.com', 'http://www.noodles.com/locations/south-end', None, 'https://vindalooindiancuisine.business.site', 'https://www.bowlero.com/location/bowlero-avondale?utm_campaign=webclicks&utm_medium=organic&utm_source=yelp', 'http://yardzatmirabelli.com', None, None, 'http://www.chefclaudio.com', None, None, 'http://rockfords.ca/', None, 'http://dannysdeli.net', 'http://www.foodcity.com', 'https://www.bnc.ca/particuliers/cartes-credit-mastercard/salon-aeroport-montreal.html', 'http://www.allforfun.ca', 'http://www.elyspringvalley.com', 'http://www.clubcorp.com/Clubs/Bear-s-Best-Las-Vegas/', 'http://www.dollartree.com/home.jsp', None, 'http://www.jriac.com', 'http://www.starbucks.com', 'http://www.cevw.com', 'http://realsh1ft.com', 'http://www.premiercustombuilders.com', '1592104749', 'http://www.scorelv.com/', 'http://bellaluna.us', 'http://www.jaaz.org', 'https://local.fedex.com/nc/charlotte/office-0746/', None, 'http://www.habibspersiancuisine.com', 'http://www.YouthfulDaySpa.com', None, 'http://morfinserv.com/', 'http://destinychurchlv.com', 'http://www.cabanasislandrestaurant.com', 'https://www.wyndhamhotels.com/hotel/46608?tel=18003370400&iata=00093785&cid=fe:bu:20170523:yl:pp:bayus:46608', None, 'http://downtowndetailslv.com', None, None, None, 'http://sonoranskydental.com', None, 'http://www.northcourtbeverage.net', 'http://www.restaurantdepot.com', 'http://www.hardrockhotel.com/las-vegas-restaurants/johnny-smalls', 'http://www.phoenixbimmer.com', 'https://azdonerightroofing.com', None, 'http://www.atozpediatricdentistry.com', 'https://www.titc.us', 'http://www.eastsidemarios.com/locations/ontario/toronto/scarborough/', 'https://www.assurant.com', 'http://www.westcheyennepharmacy.com', 'http://taylorhouselaw.com', 'http://kingsfamily.com/?utm_source=yelp&utm_medium=referral', None, None, None, None, None, 'http://romanticaboutique.ca', 'http://www.marriott.com/hotels/travel/cltcm-courtyard-charlotte-matthews', 'http://eagleriderhonda.com', None, '1592105051', 'http://www.hungryhollow.ca/', 'http://www.chandlercourtamc.com/', None, None, 'http://www.ultimatesportscards.com', '1592105091', 'https://www.arizonamovingcompanies.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282947950&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', None, 'https://calibercollision.com/locate-a-caliber-collision-center/charlotte-tyvola-rd', 'http://www.totalcigars.com', 'http://www.madisondancelife.com', 'http://www.pghgrille.com', 'http://www.allianceurgentcare.com', 'http://yafokitchen.com', 'http://www.abcautobodylv.com', None, 'http://www.boracaymassagevegas.com/', None, 'http://www.vetcoclinics.com', 'https://saharalasvegas.com/restaurants-bars/beers-and-bets/', 'http://www.robcoelectriclv.com', '1592105228', 'http://www.veneziabakery.com', None, 'http://www.summerspraytan.com', '1592105273', 'http://www.fresh-carpet-care.com/p/693?utm_source=bing&utm_medium=cpc&utm_campaign=EOW%20-%20Exact%20-%20Phoenix&utm_term=carpet%20cleaning', None, 'http://www.gordonwoodoptical.com', None, 'http://www.winghouseandsportsbar.com/', 'http://www.deltaco.com', 'https://www.obonsushi.com/scottsdale-quarter', 'http://www.valleyprotectiveservices.com/phoenix', 'http://www.wildgamegrillaz.com', 'http://thejewelers.com/venetian.html', 'http://www.sushiakaihana.com', 'http://www.wpahumane.com', 'http://menuderiaguanajuato.com', 'http://lambrettapizzeria.ca', 'http://www.clarkcountycourts.us', 'https://i-hvac.net', 'http://www.ichiriki.ca/', None, 'http://www.wordoflifelv.com', 'http://www.pizzaspano.ca', 'http://www.oakley.com/en/store-finder', None, None, None, 'http://overstockvehicles.com', None, 'http://hophausbrewing.com', 'http://www.pmilv.com', 'http://phoenixportablemobilewelding.com', None, None, 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=106&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-106', 'http://www.oldewinecellar.com', None, 'http://www.east4thstreet.com', None, 'http://www.synergyhomecare.com/agencies/az/sun-city/az02/', None, 'http://www.wildpurveyors.com', 'http://www.4monkeybusiness.com', None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', '1592105619', None, 'http://www.starbucks.com/store/14175/', None, 'https://independenceveterinaryclinic.com', None, 'https://www.choicehotels.com/CN281?mc=blypypaf', None, 'https://opasouvlaki.ca', 'https://www.lasvegassedation.com', 'http://www.mondrianscottsdale.com/mondrian_hotel_scottsdale_redbar.asp', 'http://affordablebailbondsphoenix.com/', None, None, 'http://www.todays-market.com', None, 'http://www.jazhairstudios.com/', None, 'http://www.dwellatregency.com', None, 'http://www.skinplicitylaneese.com', None, None, 'http://www.peterpiperpizza.com/', 'http://www.BlueStateElectric.com', 'http://www.thesourcemenswear.com', 'http://pizzaandbeyond.blogspot.com/', 'https://cobblestone.com/?utm_source=yelp%C3%8A', None, 'http://www.alohausedcars.com', 'https://www.carenow.com/locations/las-vegas/eastern-horizon-ridge', None, None, None, None, None, None, None, None, 'https://www.covenantcare.com/stores/silver-hills-health-care-center/', None, 'https://www.bestwestern.com/en_US/book/hotel-rooms.66086.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:66086', 'http://avolsbookstore.com', 'http://www.mrshuizenga.com/', 'https://el-mesquite-cocina-mexicana.business.site', 'http://www.arnoldcrescentanimalhospital.com', 'http://www.valorestaurant.com', 'http://www.estheticssalonandspa.com', '1592105962', 'http://www.vape29.com', None, None, 'http://www.akronmassage.co', 'https://www.eddiev.com/', None, 'http://www.lcbo.com', None, None, 'http://www.dynamitecustomsoundsolutions.com', 'http://lacubana.ca', 'http://www.juiceandjava.ca', 'http://liftedtrucks.com', 'http://www.awildhairvegas.com/', 'https://lasvegasliving.com/properties/inspire/', 'https://www.thesteelecreekdentist.com', 'http://www.abbybelladance.com', None, 'http://www.roomstogo.com/stores/pineville/carolina-place-store/1601#utm_source=yelp&utm_medium=localsearch&utm_campaign=yelp', 'http://www.scottsdaleplaza.com/dining/jds-sports-pub-en.html', 'http://www.winners.ca', 'http://www.michaelangelos.ca', 'https://www.kohls.com/stores/pa/pittsburgh-293.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://lifedesignevents.com', 'http://www.rmcf.com', None, 'http://www.nhlakesidefamilyphysicians.org/locations--hours/prosperity-church.aspx', 'http://www.friartuckonline.com', 'http://www.getacoolbox.com', 'https://www.motel6.com/en/motels.az.phoenix.18.html', 'http://www.rockerzandrollerz.com', None, 'http://www.vegasemployment.com', None, None, 'http://kahunaville.com/', None, 'http://www.bathandbodyworks.com', None, 'http://thepinkdoorcarefree.com', 'http://www.scottsdaleaz.gov', 'http://www.midibistro.ca/', None, None, 'http://www.kingdomtitle.net', 'https://www.tdcanadatrust.com/products-services/banking/index-banking.jsp', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.liveatsanmelia.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', None, 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'https://locations.monro.com/oh/bay-village/609-dover-center-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'http://www.oakridgepizza.ca', 'http://www.myspace.com/ronnieslocal069', 'http://barbershopstyles.com', None, 'http://www.spotteddogmenu.com/', 'https://www.susanvthomaslaw.com', 'https://www.rittersdinerpittsburgh.com', None, 'http://www.rocklandtrailers.com', 'http://azcustomcoatings.com', 'https://www.bannerhealth.com/locations/peoria/banner-health-clinic-vistancia', 'http://www.bestarizonacars.com', 'http://www.kay.com', 'http://www.digitaljuiceagency.com', 'http://www.bzbarandgrill.com', '1592106459', None, None, 'http://www.aspenplumbingandrooter.com', 'http://www.allcaremedicine.com/', 'http://patriatoronto.com/', 'http://www.awomansplaceobgyn.com', None, None, 'http://www.karlsqualitybakery.com', None, None, None, '1592106550', 'https://www.popeyes.com', None, None, 'http://www.michaelangelosphotography.com', None, 'https://www.wesoothesoles.com', None, 'http://www.thechickery.com/', 'http://www.dunkindonuts.com', 'http://www.treats.com', 'https://myneighborhoodprimarycare.org', 'http://www.scottsdaleaz.gov/trolley/neighborhoodtrolley.asp', None, 'http://www.lemongrassthaicafe.net', 'https://www.bowlero.com/location/bowlero-via-linda?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'http://www.framesunlimited.com/locations/shaker-heights', None, None, None, 'http://www.nicks-automotive.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.goodwill.ab.ca/goodwill-location/varsity/', 'http://www.icaptureevents.com', 'http://www.trubuildersaz.com', 'http://www.formulakartways.com', None, 'http://chandlerdrivingschool.com', 'https://www.jacksonhewitt.com/Tax-Preparation-Services-Locations/NV/North-Las-Vegas/16008/', 'http://www.sushihousebrampton.ca', '1592106768', 'http://www.thehickorytavern.com/home/hickory_tavern-locations.php?l=Charlotte+-+Providence+Rd.', 'http://www.re-wrap.ca', None, 'http://availvapor.com', 'https://threemonksandaduck.ca', 'http://www.hihealth.com', 'http://www.starbucks.ca', 'https://www.keendogtraining.com', '1592106832', None, 'http://www.kangamooplay.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://sunrisemechanical.com/areas-served/peoria-az/', 'http://www.caminoalnorteapts.com/', 'http://www.bidwellhomeimprovement.com', 'http://www.bookbeautician.com', 'http://www.marcellos.ca', None, '1592106911', 'http://www.theroyalambassador.com', 'http://nextlevelcleaners.com/', None, 'http://www.ogdenfuneralhome.com', 'https://www.starbucks.ca', None, 'http://highlifesmokes.net', '1592106971', 'http://www.goodlifefitness.com/locations/ontario/northyork/don-millseglinton?source=yelp-websitelink-northyorkdon-gl', None, None, 'https://www.elementballantyne.com', 'http://tapeface.tv', 'http://www.hussongslasvegas.com', 'http://tidycleaners.ca', 'http://www.hksarizona.com', 'http://www.prettyininkpermanentmakeupaz.com', 'http://www.thefarmersfork.com', 'http://www.ibarbieri.com', 'http://www.barbiesgrill.com/', None, 'http://www.vegasgoldbuyers.com', None, 'http://www.anthemlandscape.com', None, 'http://www.erinssnug.com/', '1592107116', None, 'http://www.gelato64.com/?page_id=409', None, 'http://mesafamilydentistryaz.com/', 'https://locations.dennys.com/OH/ELYRIA/247158', 'https://www.closetworld.com', None, 'http://segwaylasvegas.com', None, None, 'http://getahaircutlv.com', 'http://www.ticozaz.com', 'http://www.brooksdiamonds.net', '1592107221', 'http://www.giadasitaliancucina.com', 'http://stores.barnesandnoble.com/store/2680', 'http://www.bamboobistrolasvegas.com', 'http://cestbonrestaurant.com/', '1592107261', 'http://www.euro-fine.com', None, 'https://www.wrightlawnv.com', 'http://www.booksamillion.com', None, 'http://ballersbistro.com', None, None, None, None, 'http://www.bestwaypoolservice.com', 'http://www.vfwpost7401.com/', 'http://30minutealterations.com/', 'http://www.auroranaturalmedicine.com', 'http://littlecaesars.com/', None, 'http://www.yaymaker.com', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.SecureDataRecovery.com/Charlotte', 'https://smartstopselfstorage.com/storage-locations/usa/nevada/las-vegas/smartstop-self-storage-4851-e-bonanza-rd', 'http://phoenixarc.salvationarmy.org', 'http://www.timbermesaoutdoors.com', '1592107451', 'https://www.chilis.com', 'http://www.phoenixvirtualtour.com', None, 'http://gorgeouslady.ca', 'http://www.tinderboxcigars.com', None, 'https://primpandblow.com/locations/primp-and-blow-chandler/?UTM=yelp', None, None, 'http://www.aladorpetresorts.com', 'http://www.bcbg.com', 'http://feelslikehomefarm.com/index.html', 'https://www.circlek.com/store-locator/us/ruskin/3602-hwy-41-s/2707247', None, None, None, None, None, 'http://www.kazesushi.ca', None, None, 'http://www.fabulousmanicurebar.com', 'http://www.gtatireandauto.com', 'http://www.mannyforinsurance.com/?cmpid=UGOG_BLM_0006', 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', 'http://www.torontoairportlimo-taxi.ca', 'http://Www.FlamingoCoolsVegas.com', 'http://www.secondcup.com/location/toronto-355-danforth-avenue', 'http://www.jdbyrider.com/buy-here-pay-here-pittsburg-monroeville-pennsylvania-pa114', 'http://www.djinlasvegas.com', 'http://freshco.com/stores/bloor-dundas', 'http://www.totalwine.com/store-info/arizona-phoenix-desert-ridge/1003', 'http://www.ggfarm.com/welcome-to-grateful-growers/harvest-moon-g', None, 'http://www.apassionforpetssalon.com', 'http://www.trulythaicuisine.com', 'https://www.scottsdalecfdh.com', 'https://www.legendatarrowhead.com', 'http://vehiclesunlimitedinc.com', 'http://vegasairduct.com', None, None, 'http://www.thetcmclinic.com', None, 'http://www.verizonwireless.com/stores/colorado/denver/16th-st-mall-201560/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://www.plazaloftskierland.com/', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'https://www.neohioeyes.com', 'https://www.enterprise.com/en/car-rental/locations/us/az/tempe-holdeman-5015.html?mcid=iyp:8368400', 'http://www.chelseanicole.com', 'http://www.morningsidenissan.com', None, '1592139482', None, 'https://www.marriott.com/hotels/hotel-information/restaurant/yyzsb-delta-hotels-toronto-east/', '1592139508', None, 'https://www.chocolatebywickerhead.com', None, '1592139537', None, 'https://www.kneadtodestress.com', '1592139573', 'http://www.holeeburger.com/', 'http://www.gttdogs.com', None, 'https://www.faded.club', None, 'http://www.autoberry.ca', None, 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=441', 'http://www.pandaexpress.com/', 'http://www.mistyglenkennel.com', 'http://www.krispykremeaz.com', 'http://nsbank.com/', '1592139673', 'http://www.vivefitness.com/', 'http://www.mchair.com', 'http://purefitnessclubs.com/', 'http://www.bstreetrmt.com', 'http://www.rungreatrace.com/', None, 'http://lasvegas.777rentals.com', 'http://www.philipamodei.com/lasvegashairstudio/contact', 'http://www.moongsushi.com', 'http://www.capitalone.ca', '1592139757', 'https://www.discounttire.com/store/az/scottsdale/s/1284?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://www.cmgfi.com/agents/richard-blair', None, '1592139794', 'http://www.lvboneandjoint.com', None, 'http://www.eatgarbanzoaz.com/', None, None, None, 'https://lumenbrite.com/locations/phoenix/', 'http://www.Topspizza.ca', None, None, None, 'http://chefkennysasianvegan.com', None, 'http://www.safestoreaz.com', 'http://www.foothillsrehab.com/', 'http://www.25thstreetautomotive.com', 'https://cobblestone.com/?utm_source=yelp%C3%8A', '1592139942', None, 'https://www.bankofamerica.com', 'https://www.purebarre.com/location/westlake-avon-oh', 'http://www.tigerslairaz.com/', None, 'http://adavenkid.com/', 'http://www.shoregrillandgrotto.ca', None, 'https://www.advancedfootankle.com', 'http://www.insideoutsports.com', 'http://roysliquor.com', 'http://www.bestchoice4insurance.com', 'http://www.redkphoto.com/', 'http://www.firstchoicedental.com/locations/sun-prairie-office', None, 'https://www.target.com/sl/henderson-lake-mead-pkwy/2404', None, None, '1592140058', 'http://substationaz.com', 'http://searchthec4group.com', None, 'https://www.zimbrickaudiofmadison.com', 'http://www.mercuryautospa.com', 'http://mtclaret.org', None, 'https://www.nothingbundtcakes.com/bakery/nv/las-vegas-eastern?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=las-vegas-eastern_2', 'http://bobbyqgrill.com/', 'https://www.spring-green.com/franchise/urbana-area/', 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/etobicoke-(1).aspx', 'https://www.kohls.com/stores/az/scottsdale-620.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'https://www.abovegroundartsupplies.com/', None, '1592140190', None, 'http://www.brighterangels.com/phoenix.html', 'http://croywifi.com', 'http://www.jlbridal.com/', 'http://www.thepaperytoronto.com', 'http://brocach.com', 'http://www.balancingyourchemistry.com/', 'http://deeplyrootedhairstudio.com', None, 'http://www.chennaichettinaadpalace.com', None, None, '1592140276', 'http://gohomeplate.com', '1592140287', 'http://www.lvac.com/locations/central', 'http://www.amici-dinos.com', 'http://greenfieldjewelers.com', 'http://oldnavy.gap.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.spoonandfork.ca/spoon-and-fork-eglinton/welcome', None, 'http://fpcmesa.org', 'http://www.goodlifefitness.com', 'http://www.theecigflavourium.com', 'http://www.milagrorestaurant.com', None, 'https://www.thingsremembered.com', None, 'http://www.sambabraziliangrill.com/', None, None, 'http://fusionpowerco.com', 'http://www.michaelkors.com/', 'https://shop.lululemon.com?CID=ps_YELP_website_org', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://agents.farmers.com/az/tempe/greg-krajewski?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'https://www.sephora.com/happening/stores/pittsburgh-shadyside', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://skyvapeaz.com', 'https://pablocanada.com/shop/', 'http://www.nationalcarmart.com/', 'http://home-savings.com', 'http://chopstickexpresstogo.com', 'http://www.pathwayscounselingsvcs.com', 'http://www.petsittingscottsdale.com/', 'http://www.woodbridgevacuum.ca', 'http://www.golfwildhorse.com/', 'http://www.jennysdispensary.com', None, 'http://thericegarden.com/', None, 'https://locations.jackinthebox.com/us/nc/charlotte/7725-pineville-matthews-rd', 'https://performancetherapymassage.net', 'http://www.shinbay.com', 'http://www.solapizza.com', 'http://www.gilbertserenitydental.com/', 'http://jollyrollsicecream.com', 'http://browsbyhilary.com', None, 'http://www.adventdentistry.com/', 'http://www.mastersgalleryltd.com/', 'http://smog-king.com', None, None, None, 'http://www.a-ztennis.com', 'https://www.cellairis.com/gilbert-cell-phone-iphone-repair-yelp', 'https://made-in-argentina-la-esquina-argentina.business.site', None, 'http://www.mustardseedherbary.com', None, 'http://ivorystar.com/shows/friends-the-musical-parody', None, 'http://FoxtailLasVegas.com', 'http://www.starbucks.com/store/1006250/ca/jean-adam-st-denis/75-avenue-de-la-gare-saint-sauveur-qc-j0r-1r6/les', 'https://www.plumbcrazy4plumbing.com', 'https://www.enterprise.com/en/car-rental/locations/us/al/huntsville-madison-55ha.html?mcid=iyp:8368400', 'http://gamblerscafe.com', None, None, 'http://www.themachatgroup.com', 'http://www.mikesbarbershopmentor.com', '1592140868', None, None, 'http://chaseanddestroy.com', None, None, 'http://andersonac.com', None, 'http://www.phoenixazchinesefood.com', None, 'https://www.allnevadainsurance.com', 'https://thepolishedbrow.com', 'http://muramoto.biz', 'https://palmbeachtan.com/locations/OH/Westlake-Detroit-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=CLE', '1592140999', None, 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', None, 'http://www.campusbodysalon.com', 'http://www.lovesick.com/store-details?StoreID=9020', 'https://www.infinityfinancialmortgagecorp.com', 'http://www.atlwingsyourway.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.lvatvtours.com/', None, None, None, '1592141121', 'http://www.psychiatrylasvegas.com', 'http://www.all-starpediatrics.com', None, 'http://roomofonesown.com/', 'http://www.unityrideshop.com', 'http://villemontpizza.com/index.html', 'http://www.2bmod.com', '1592141176', 'http://washworkslaundry.com', 'https://highweedmedshop.com', 'https://mrsub.ca', 'http://gradeaid.ca', None, None, None, None, 'http://www.mrrooter.com/phoenix', None, None, None, 'https://www.sheetz.com', None, 'https://www.wyndhamhotels.com/hotel/36226?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:36226', None, 'https://www.coffeebean.com/store/usa/scottsdale/promenade-at-scottsdale', 'http://www.clearwash.ca', 'http://www.carolinavaluevillage.com', 'http://www.sincitycrossfit.com/', None, 'http://www.epennzoil.com', 'http://www.bojangles.com', 'https://www.americafirst.com/about/branches/branch-details.cfm?siteNo=233', None, 'https://www.sprint.com/storefronts/bd/sprint-south-euclid-oh-44118-fcs-1799/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://townhall.innis.utoronto.ca', 'http://www.azgreencleaning.com', 'http://pa.pittsburgh.charmingcharlie.com/fashion_accessories_pittsburgh_pa_128.html', None, 'http://www.kickaxeguitars.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YULRI', 'http://www.sunlessboutique.com/', 'https://www.dominos.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://redhousepub.co', 'http://zellaspizza.com', 'http://www.palminaleone.com', 'http://comicgirlcoffee.com', 'http://www.andreawhitten.com/', 'https://www.whitakertire.com/location/mode/1/3701-greensprings-ave-west-mifflin-pa-15122.aspx', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.taylorrentalavon.com', 'http://www.starbucks.com', None, None, 'http://www.urbanaparks.org/facilities/16.html', 'http://www.superdry.com/', '1592141552', None, 'http://hazelgeneralstore.com/', 'https://www.supercuts.com/locations/az/glendale/bell-park-shopping-center-haircuts-80215.html', 'http://www.creativetraveler.com', None, None, None, 'http://www.circabella.com', '1592141628', None, 'http://www.usps.com', 'http://www.aaronbrothers.com', 'http://www.roastmadison.com/', 'https://www.americancampus.com/student-apartments/nc/charlotte/university-crossings-charlotte', 'http://calgary.cnty.com/', 'http://locations.michaels.com/AB/CALGARY/3902/', 'http://www.home-computerhelp.com', 'http://www.thebeverleyhotel.ca', None, 'http://sachisalon.com', None, 'http://www.durafastlabel.ca', 'http://www.vegas-salon.com', None, 'http://firstchurch.church', None, 'http://www.sumitsyoga.com', 'http://www.popeyeschicken.ca', None, 'https://kneaders.com', 'https://www.turkishkebabhouse.net', None, 'http://www.subarusaintejulie.com/en/', 'http://www.eyelidsphoenix.com', 'http://www.victoriassecret.com', None, 'http://totalwellnessacupunctureaz.com/', 'http://www.maxandermas.com/locations/333038', None, 'https://www.berkshirecommunities.com/apartments/nc/charlotte/berkshire-dilworth/?utm_source=Yelp&utm_medium=Referral', 'https://www.walmart.com/store/2050/henderson-nv/whats-new', None, 'http://www.discounttirebellevue.com/', 'http://www.pizzanova.com', 'http://www.7-eleven.com/?yelp=29384', None, None, 'http://www.marriott.com/hotels/travel/yyzmk-courtyard-toronto-markham/', 'https://locations.levi.com/nv/lasvegas/denim_las-vegas_nv_188.html', 'https://www.pizzahut.ca/store-details/store-R32814/pizza-hut-Mississauga', 'http://www.onpointhairandnail.com', None, None, 'http://www.climatechnc.com', None, 'http://www.newgalleryofmodernart.com', None, 'http://www.assemblychefshall.com', 'http://www.wisconsincheesemart.com', 'http://www.gamestop.com', None, 'https://flights.hisgo.com/us/', 'http://www.starbucks.com/store/14887/', None, 'http://www.belgo.ca/', None, '1592142134', None, 'https://www.lasvegasbookkeeping.com', 'http://www.dollarama.com/', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'https://www.instantplumbing.ca', 'http://www.tintaz.com/', 'http://www.aneyefordetail.com', 'http://vanlanendds.com', 'http://www.loonspub.com/', None, '1592142216', None, '1592142226', None, 'https://www.bigfrog.com/stores/gilbert-az/', 'http://csrcoffee.com', 'http://www.expert-locksmith.ca', 'http://www.manhattanfishgrill.com', 'https://henleysfloor.com', None, 'http://www.skallywagcigars.com', 'http://www.speedandstrengthuniversity.com', 'http://www.lasvegasrestorationllc.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', None, 'http://steelecreekpediatricdentistry.com', 'http://www.mesafarmersmarketandflea.com', None, 'http://theforumatdesertharbor.com', None, 'http://addisonparkapts.com?utm_source=Local%20Listings&utm_medium=referral&utm_campaign=Top%20Line%20Local', 'http://www.greatclips.com', None, 'http://www.citi.com', None, None, None, None, None, 'http://www.7baker.ca', 'https://team-kaizen.com', None, 'https://donroyaldrycleaner.wixsite.com/website', None, 'http://www.goldstartailoring.com', None, 'http://www.planetfitness.com/gyms/charlotte-whitehall-nc-125?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.gerrysmarine.com', None, None, 'https://www.suretempair.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/oh/elyria-3931.html?mcid=iyp:8368400', 'http://www.krispykremeaz.com', 'http://www.breadandcircus.ca', None, 'https://www.millerstavernlv.com', 'http://www.marcs.com/stores/marc-s-lakewood-grocery-store-44107.aspx', 'http://www.ambrosia.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.awardscheesecakes.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FMSNCY', 'http://www.daleskarrparts.com/', 'http://www.bp.com', None, None, 'http://magictailor.ca', 'http://www.distillerypub.com/', 'http://www.deckscapes.com', 'http://www.chromasalonandboutique.com', 'https://www.bfly.ca/experience-bfly/', 'http://www.thrill-bikes.com', '1592142722', None, 'http://www.gotransit.com/publicroot/en/travelling/stations.aspx', 'http://ModManBarber.com', 'https://chocolateshops.sees.com/az/phoenix/chocolate_shops_phoenix_az_102103.html', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://sunboxphotography.biz', None, 'https://locations.monro.com/oh/painesville/1575-mentor-avenue?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', '1592142811', 'http://www.truemedispa.com/', 'http://www.realfruitbubbletea.com', 'https://az.aaa.com/agent-office-locations/az/phoenix/aaa-phoenix-office', None, 'http://jeroldoptical.com/', 'http://www.redrocklasvegas.com/dining/hachi.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=RR&utm_content=RR-PROPERTIES&utm_campaign=RR-YELP', 'http://jenniferwallens.com', None, 'https://clevelandhungarianmuseum.org', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.lakenormanchrysler.com', 'http://latitude360.com/pittsburgh-pa/', 'http://www.brewercommercialservices.com/', 'http://www.winerack.com', None, 'https://www.radisson.com/madison-hotel-wi-53719/madison', 'http://cityofhenderson.com/henderson-happenings/facilities/recreation-centers/whitney-ranch-recreation-center', None, 'http://Terminalbarbershop.com', None, 'http://www.americanapparel.net', None, 'http://www.mariospgh.com/southside/', 'http://www.shamrockroofingservices.com', 'https://www.amctheatres.com/movie-theatres/phoenix/amc-ahwatukee-24?utm_uid=yelp', None, '1592146361', 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store97', 'http://meineke.com', 'http://www.partydesignlv.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.margaritavilleglendale.com/', 'https://www.chimneystax.ca', 'http://www.palmettofamilyhearing.com', 'https://airpromaster.com', 'http://www.fresh-burger.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281380115&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://tempecomputerrepairservice.net', None, 'https://www.lvaspensalon.com', 'http://www.pacetax.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/13777+Pearl+Road-Strongsville-OH-44136/storeid=4300?cid=ps_ylp_2020', None, None, 'http://www.pandalawfirm.com', None, None, 'http://www.dominos.com', 'http://www.azuldayspa.org', None, 'http://www.koa.com/campgrounds/madison/', 'https://tinylovesphotography.com', 'https://www.imyourmechaniclv.com', 'http://www.moes.com', 'http://eng.bigbustours.com/lasvegas/home.html', 'http://www.lindleylawoffice.com', 'http://www.actiontours.com', None, 'http://www.thaizone.ca/', 'https://www.islandthymepub.com', None, None, 'https://www.efirstbank.com/customer-service/find-location.htm?loc=BELL', None, 'http://sagoautoglass.com', 'http://www.truevalue.com', 'http://www.clemcopostal.com', 'http://www.barrymorefurniture.com', 'http://www.plazahotelcasino.com/entertainment/superstars_of_magic', 'http://www.peakchiropracticpgh.com/', 'https://locations.sonicdrivein.com/nv/lasvegas/6301-w.-lake-mead-blvd..html', None, None, 'http://www.scooopskidspa.com/', 'http://www.ladybugsandwiches.com', None, 'http://www.separkmansion.com', 'https://www.ironwoodcrc.com/locations/?locations_doc=scottsdale', 'http://www.goldenlobsters.com', 'http://www.FourSonsLandscaping.net', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/north-toronto-eglington-yonge-c245.html?mcid=iyp:8368400', 'https://www.softsurroundings.com/stores/the-district-at-green-valley-ranch/', 'http://wellnesslasvegas.com', 'http://www.southernshows.com/wch', 'http://omfastfoodrestaurant.com/home.html', 'http://fuerstauto.com', 'https://www.papamurphys.com', None, None, 'http://eeleconomicrestaurantequipment.com', 'http://www.haircoloringinphoenixaz.com', None, 'http://www.oakesappliance.com', 'http://whasn.com/providers/julie-goodell', 'http://www.huntersvilleford.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.carminespizzakitchen.com', 'http://www.homedepot.ca', 'https://www.hendersonmentalwellness.com', None, 'http://onetoone.case.edu/', 'http://www.taqueriapastorcito.com', 'https://www.bakerbros.com/visitus', None, 'http://www.fallsheating.com/', None, 'http://www.starbucks.com', None, None, 'http://houlihans.com/', 'http://www.yogurtini.com', 'http://www.donvalleynorthlexus.com', 'https://www.smartstyle.com/en-us/locations/az/phoenix/located-inside-walmart-2113-haircuts-11301.html', None, 'http://www.bk.com', None, 'http://pizzabytheslice.ca/', 'http://www.shapetrain.com', 'http://coronadelsolhighschool.net/', None, None, 'http://www.wyattworks.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1015+East+Ray+Road-Chandler-AZ-85225/storeid=7849?cid=ps_ylp_2020', 'http://massageaddict.ca/oakville', 'http://Inspiradabarberandbeauty.com', 'http://www.nuvohotel.com', 'https://www.hilton.com/en/hotels/lasruru-tru-las-vegas-airport/?SEO_id=YELP-RU-LASRURU', 'http://www.starbucks.com/store/9059/', 'https://azoralsurgery.com', 'http://www.bethanyanimalhospital.com', None, 'http://www.goodeggdining.ca', 'http://www.nevadadivorce.net', None, 'http://www.classykitchenandbath.com', '1592147262', None, 'http://www.service1stenergysolutions.com/', 'http://www.vesperrx.com', '1592147301', 'http://www.chestnuthillsdental.com/locations-providers/pittsburgh-shadyside/', 'http://www.macssushi.com', 'http://www.nanashake.com', 'http://www.eyepriority.com', 'http://www.northcoastbodymod.com', None, '1592147361', 'http://www.lvcc.com', 'http://storelocator.pepboys.com/pepboys/stores/phoenix/cactus/00747', 'http://www.reginospizza.com', 'http://www.travelbughealth.com', None, None, 'http://www.mysisterscloset.com/', 'http://www.carolsconfectionspgh.com', 'http://www.altaderm.com', 'https://www.ymcacalgary.org/program-descriptions/locations/brookfield-residential-ymca-at-seton/', 'http://www.aaaonestopappliance.com', 'https://www.tonysautoshop.com', 'https://911drivingschool.com/ohio/driving-school-rocky-river-ohio/', 'http://www.gaudinporschelv.com', None, 'http://www.tuesdaymorning.com', 'http://www.tlcflooringlv.com', 'http://www.buddystubbshd.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'http://www.potterlawaz.com', 'https://www.maaco.com/locations/nc/charlotte-11619/', 'http://www.bartendingschoolc2c.com', 'http://www.millenniumsalonmadison.com', 'http://www.yak.com', 'http://rackempubandbilliards.com', 'https://restoreandrenewmassage.com', 'http://creativeillusionshairstudio.com', 'https://www.TheUltimatePartyStore.net', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.completevisioncare.com/home.html', None, '1592147593', 'https://www.northwest.com', 'http://www.arizonalullabyguild.com', 'http://www.meltwich.ca/richmondstreet/', 'http://www.aroundtheblock.com', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700006435131063&ds_s_kwgid=58700000444951711&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', '1592147657', None, None, 'http://www.littlecaesars.com/', None, 'http://cherryboomboom.com', None, None, 'http://www.azdivalashes.com', None, 'http://www.drteddysim.com/about-dr-teddy-sim/', 'http://access-handyman.webnode.com', None, 'http://www.roomforhealth.com/', 'https://www.autozone.com/locations/nv/las-vegas/1351-n-eastern-ave.html', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'https://www.salt-tempe.com', 'https://nature.discoveryplace.org', 'http://www.senjivastudio.com', None, None, None, 'https://www.shijosushi.ca', None, None, 'http://www.qinthaicuisine.com', None, 'http://www.invisiblehandyman.com', None, None, 'http://headtripbrewery.com', None, None, None, 'http://www.444park.com', 'http://www.pueblomedicalimaging.com', 'http://www.the-bag-lady.biz', None, None, None, None, 'http://www.bbqisland.com', 'http://www.ohiocitynails.com', 'https://www.realstar.ca/apartments/on/brampton/188-cityview-apartments/index.aspx', None, 'http://walmart-eyedocs-lasvegas.com/Marks-Sunset', 'https://studios.waxingthecity.com/ll/US/PA/Pittsburgh/3605-Butler-Street?utm_source=yelp&utm_medium=local&utm_campaign=localmaps', None, None, 'http://omnidermatology.com', 'http://locations.in-n-out.com/234', 'http://www.eastvalleyfiduciaryservices.com', '1592148033', 'https://azflorist.com', 'https://www.meineke.com/locations/pa/pleasant-hills-2517/?utm_source=yelp&utm_medium=xvc', 'http://www.ezpoolslv.com', None, 'http://alluregardens.com/', 'http://abovethecrustpizza.com', 'http://www.alldogsgotobev.com/', '1592148088', 'http://itdotrepairs.com', None, None, 'http://www.uwhealthkids.org/locations/kidsdetail.jsp?locationId=59', None, 'http://www.visiblevoicebooks.com', 'http://www.juvenaspa.com', 'http://www.aeortho.com', 'http://www.rosestodaylasvegas.com/?srccode=yelp_track', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.charakcenter.org', None, 'http://gear-oh.com', 'http://www.wfamilydental.com', 'http://salonstylush.com/', 'http://www.westaddisonaz.com', '1592148259', 'https://www.barra-sandusky.com', None, 'http://www.denturerepairinglendaleaz.com', None, None, 'http://www.schneidersauto.com', None, 'https://datarecovery.com/about/toronto/', 'https://stores.jcpenney.com/az/phoenix/clothing-stores-phoenix-az-2889.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2889', 'http://www.picknsave.com', None, None, None, 'https://www.eliminexpest.com', 'http://www.starbucks.com/store/9298/', 'http://www.lightrx.com/mesa', 'https://local.biglots.com/pa/monroeville/1960?zcp=pd_local_yelp', None, 'http://rizzosspaghettihouse.com', 'https://www.statefarm.com/agent/US/NV/Henderson/Carl-Endorf-HYSY71YS000?cmpid=ST0N_BLM_0006', '1592148451', 'http://www.lveyedocs.com', 'https://www.usps.com/', 'http://www.fatbastardburrito.ca/locations/burrito-whitby', None, None, 'https://www.scottsdale-duilawyer.com/?utm_source=scottsdale_location&utm_medium=yelp&utm_campaign=website_link_click', 'http://arizonapianomover.com', None, 'http://www.ctrglass.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, None, None, 'http://www.rollcare.ca', 'https://locations.panerabread.com/wi/fitchburg/2960-cahill-main.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', None, 'http://www.speedlube.net', 'http://local.skechers.com/ca/glendale/38/', 'http://www.lowes.com', 'https://www.pinnaclenissan.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'https://www.ulta.com/stores/westlake-oh-1423', 'http://www.azphi.com', None, 'http://www.lacasadelahabana.com', None, None, None, 'https://www.ediblearrangements.com/fruit-arrangements?utm_source=Yelp&utm_medium=Listing&utm_campaign=StoreID206', None, '1592148696', None, None, 'http://www.starbucks.com', '1592148737', 'http://www.getenzo.com', 'http://howlerspittsburgh.com', None, None, None, 'http://l.macys.com/fashion-show-in-las-vegas-nv?cm_mmc=Yelp_Stores-_-LasVegas-_-n-_-532&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Las+Vegas_532&m_ac=yelp_stores&m_ag=n', None, None, None, 'https://local.safeway.com/safeway/az/scottsdale/23565-n-scottsdale-rd.html', 'http://local.firestonecompleteautocare.com/arizona/cave-creek/4915-e-carefree-hwy/?lw_cmp=IYP_YPC_MLP_784291', 'http://www.doordoctor.ca', 'https://www.maccosmetics.com', None, 'http://www.popularpizza.ca/locations.phtml', None, None, None, None, 'http://www.craftcellars.ca', 'http://www.valleylights.com', 'http://www.quickspark.com', 'http://www.atlwings.com', None, 'http://www.OnTheSpotLV.com', None, '1592148965', 'http://www.hillsong.com/phoenix', None, None, 'http://www.divinethreading.com', 'http://www.mayfieldohdentist.com/', 'http://www.scottsdaleaz.gov/sports/aquatics/mcdowell-mountain-ranch-pool', None, 'http://www.ryah.ca/', None, 'http://www.bubblesandbowslv.com', 'http://www.houdini.com', None, None, 'http://mmgyn.com', None, 'https://www.openriceclt.com', 'http://www.mccoolspools.com', 'http://musiccentrecanada.com/', None, 'http://www.gioninos.com', 'http://www.ericpalacioslaw.com', None, 'http://www.embassygrand.com', 'http://www.firstprimerealtygroup.propertyware.com', 'http://www.sierraironlv.com', None, None, '1592149192', None, None, 'https://www.bakerbros.com/glendale', 'https://prairieflowersandgifts.com', 'https://www.sunsetgrill.ca', 'https://americanbuilderslv.com', 'https://www.petsfriend.ca', 'https://cobsdoggersandmore.wixsite.com/website', 'http://jacksaloon.com', 'http://www.thesweetpotato.ca', None, None, 'http://www.breatherefuge.com', None, 'http://www.fantasticsams.com', 'http://www.olsonortho.com', 'http://www.bulldogliquidators.com', 'http://www.ladyyorkfoods.com', 'http://storelocator.pepboys.com/pepboys/stores/las_vegas/east_charleston/00685', 'http://www.acaringnanny.com', 'http://www.markhamtheatre.ca', None, None, 'http://www.mermaidsplashnails.com', 'http://www.stephanoslv.com', None, 'https://www.peppywalnutssweetsboutique.com', None, 'http://www.courtesychrysler.com', 'http://creamistryAZ.com', 'https://www.skininjectables.com', 'http://www.lcbo.com', 'https://www.sprint.com/locations/nv/henderson/334-w-lake-mead-pkwy', None, 'http://nourishmassageandskincare.com', 'http://www.timhortons.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044280206066&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://sidelinestreeservice.com', None, 'http://www.evooristorante.com', 'http://www.budacafe.ca', 'http://leesliquorlv.com/locations/sunset-office/', None, 'https://www.jackentertainment.com/thistledown', 'http://www.orangetreepools.com', 'http://www.panorea.ca', 'http://www.cancleanpros.com', 'http://www.phxestatesales.com/', 'http://www.bareoaks.ca', 'http://www.marriott.com/hotels/travel/phxss-springhill-suites-phoenix-north/', 'http://steviespizza.com', 'http://www.7-eleven.com/?yelp=32265', 'http://tricitytowingaz.com/', 'http://www.vanillabeanonline.com', 'http://www.haggen.com', 'https://www.thebrick.com', 'http://www.appleplumbingaz.com/', 'https://www.americaroofingco.com', 'http://www.broadacresm.com', 'http://www.MobileDogWash.dog', None, None, 'http://www.cozymels.com', 'https://cacao70.com/fr/nos-emplacements/atwater', 'http://www.randstadusa.com/', None, 'http://www.soulas.ca', 'http://www.masalahousepgh.com', 'http://www.creativeformalwear.com/', None, 'http://annandalegolfclub.com/', 'http://drmikepace.com', None, None, None, 'http://www.rona.ca/', 'https://www.riosbraziliansteakhouse.com', 'http://johnnyrockets.com', None, None, 'https://www.goldencorral.com/locations/970/golden-corral-william-penn-highway', 'http://www.glendaleaz.com/parksandrecreation/ThunderbirdPaseoPark.cfm', 'https://www.daveandbusters.com/locations/pineville', '1592150792', 'http://whatisbrewing.com', None, None, 'https://www.klinkecleaners.com/locations/dane-county-locations/monroe-street', 'http://www.ymcacharlotte.org', 'http://vegasvisionoptometry.com', 'http://www.photoandgo.com', None, 'https://the-post-sports-bar.business.site', None, None, 'https://www.chevronwithtechron.com', 'https://www.audioexpress.com/locations/15115-n-hayden-road-scottsdale-az-85260/', 'http://www.kidsgardenlearningacademy.com', 'http://www.iamyoga.ca', 'http://vmacauto.com', None, None, None, 'https://www.mansion54.com', 'http://www.gogopokeus.com', 'http://www.allen-equipment.com/', 'http://tandoorigrillcalgary.com', 'http://www.indulgeculinaryacademy.com', 'http://pillartopost.com/', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=13080', None, 'http://siestalandscaping.com/index.html', 'http://storelocations.ae.com/us/pa/pittsburgh/540-south-27th-street.html', 'http://www.rockstartattoolasvegas.com', None, None, 'http://logansroadhouse.com', '1592150921', None, 'http://www.villageatcobblestonecourt.com', 'http://www.burritogordito.ca', 'http://www.tigbbqlv.com', 'http://www.fishfurniture.com', 'http://www.windowandsolarservices.com', 'http://www.pazzopittsburgh.com/', None, 'http://www.richardstreeservicellc.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://sabalimo.com', None, 'http://www.parkway-sc.com', '1592150982', 'https://www.schlotzskys.com/wisconsin/madison/1532', 'https://stores.anntaylor.com/az/scottsdale/7014-east-camelback-road.html', None, None, 'https://www.wingstop.com/location/wingstop-1394-gastonia-nc-28054/menu', None, None, 'http://www.calgarytransit.com', 'http://www.zeebasleep.com/', 'http://camdenlv.com', 'https://chicagoschickenandwafflescle.com', 'http://www.performancemarineaz.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.starbucks.com/store-locator/store/1016078', 'http://www.mullinspub.com/locations/kington-road/hours-location/', 'http://www.christensenoralsurgery.com', 'http://www.med-place.org', 'http://www.goodearthcafes.com', 'http://www.jkhlawoffice.com', None, None, 'https://prolinewindowtint.com', None, None, 'https://dainties-macaron.business.site', 'http://www.abovebeyondcleaner.com', 'https://www.petsmart.com/stores/us/oh/macedonia-store1851.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', None, None, 'http://www.heartcenterofnv.com', 'http://www.zaksbicycleshop.com', '1592151104', '1592151108', 'http://nevadaorthopedic.com/directory/people/show/thomas-vater', 'http://www.pastelesmary.com/', None, 'http://www.sciullos910.com/', 'http://www.simplyflowersnthings.com?srccode=yelp_track', 'https://www.sonoranspine.com', None, 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', None, 'https://www.wellsfargo.com', 'http://www.weymouthfarms.com', 'http://shawarmaxpress.ca', 'http://thebarrelpub.ca', 'http://www.eurekagifts.com', None, 'https://chatters.ca/stores/chatters-square-one/', None, 'http://www.lviglobal.com', 'http://hamptoncrestenc.com', 'https://www.saucepizzaandwine.com/locations/tempe-tempe-union/', None, None, 'http://tandooristyle.ca', 'http://www.associatedretinaconsultants.com', 'http://www.azeuros.com', None, None, None, 'https://www.supercuts.com/locations/az/peoria/north-valley-power-center-haircuts-82958.html', None, None, 'http://www.chassepermanentmakeup.com', 'https://www.expressoil.com/stores/gilbert/az/3502/', None, 'http://www.bestmatt.com/', None, 'http://www.nonnasplace.ca', 'http://www.commonwealthah.com', 'http://www.cigna.com/cmgaz/locations/phoenix-central-multi-specialty-center', 'http://www.safeway.com', 'http://www.roxxsouthend.com', 'http://www.torontohearingservices.com/location-contact/north-york-ontario-ca/', 'http://www.cookiedoughjo.com', 'http://www.nohiddenfeestickets.com', None, 'https://www.simon.com/mall/southpark', 'http://kintarooh.com', None, 'http://nahasushi.com/', None, 'http://www.princessauto.com', 'http://2ndandcharles.com/', 'http://www.NorterraAH.com', 'http://www.torontomenssuits.ca', 'http://www.metalmorphosis.tv', 'https://homewoodfamilyaz.org', None, 'http://www.bestpittsburghhomes.com', 'http://www.awhlawyers.com', None, None, None, None, 'http://www.rightbynaturemarket.com', 'http://www.centrooptical.com/', 'http://www.grodzinskibakery.com/', 'https://www.spoonerpt.com/locations/goodyear/', None, 'http://www.detailingknights.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.secondcup.com', None, 'http://tinyurl.com/hp44240', 'http://tokyogrill.business.site', None, 'http://www.scoopspittsburgh.com/', None, 'http://www.candlelightersnv.org/', 'http://www.grapevinewinebar.com/', 'https://www.torrid.com/store-details?StoreID=5371', 'https://freedsbakery.com/pages/freeds-dessert-shop', '1592151332', None, None, 'http://www.pandysgardencenter.com', 'http://petgrooming-charlotte.com', 'http://southlandlanes.com', None, None, None, None, 'http://www.truenorthbarbers.com', None, None, '1592151370', '1592151372', 'http://www.sunsolarsolutions.com', None, 'http://www.avenuediner.com', 'https://www.hubbardswim.com', 'http://www.canamrealestateservices.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.dreamdealers.com', None, 'http://www.rapidcollision.com', None, 'http://www.homesteadmaid.com/', 'http://www.jackinthebox.com/', 'http://www.doylechiropractic.com', 'https://dutchbros.com/?utm_source=phoenix&utm_medium=yelp&utm_campaign=website_phoenix', 'http://www.spookyfast.com/', 'http://popeyeschicken.ca/', None, 'http://huntfamilychiro.com', 'http://www.stafflink.ca/', '1592151421', None, 'https://dc-glass-glass-repair-service.business.site', 'http://www.ohiocitypizzeria.org', 'http://www.northyorksheridanmall.com', None, 'http://www.concretemadenew.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.samscyclesupply.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://graphicideals.com/', None, 'https://www.excellenceairllc.com', 'http://www.larryjsauto.com', None, 'http://www.gioninos.com', None, 'https://www.pridestaff.com/tempe', 'https://www.cinemark.com/nevada/century-orleans-18-and-xd', None, 'https://thepetclub.net', None, 'http://www.thedartshop.com/', 'https://www.greentreesportsplexpittsburgh.com', 'http://safe.frontpointsecurity.com/yelpsecurity-us', 'http://www.themagicoflearning.com/', 'http://www.westvalleyent.com/', 'http://www.lvccld.org', 'https://pizzeriamoretti.com/moretti-toronto/', 'http://www.crossfitmte.com', 'http://mcmurraych.com', 'http://murderinkproductions.com', 'http://baskonseaboard.com/', 'http://www.gracefulcakecreations.com/', 'http://www.clasensbakery.com/', 'https://jessicanailinc.wixsite.com/feelingnailsandspa', None, 'http://www.mrlube.com/en/mr-lube-near-you/Locate-a-Mr-Lube/richmond-hill-1070-major-mackenzie-drive-east.aspx?storeid=190&postalcode=L4S%201P3', 'https://www.tacobell.com/food?utm_source=yelp&utm_medium=social&utm_campaign=yelp-pilot-test-menu-static-1-CS&utm_content=paid', 'https://www.charlotteautodetailingservices.com', None, 'http://www.helzberg.com', 'http://www.haircutsarefun.com', 'http://lasvegasyardwork.com', 'http://www.innevation.com', 'https://www.cox.com/local/residential/stores/nv/henderson/545-marks-street?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q102', 'http://www.nesbitslanes.com', None, 'http://www.eggsmart.ca', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.artistictlc.com', 'http://www.wendys.com', 'https://www.haggardchiro.com/chiropractor-phoenix/', None, 'http://www.starallison.com', 'http://www.pupusaslafamiliar.com', 'http://usonv.com', 'https://www.devadave.com', 'http://www.evdi.com/?location=chandler', 'http://www.raulsoriginal.com/', 'http://www.omasplaceaz.com', 'http://www.legacynails.net', '1592151592', 'http://www.rvvh.ca/', 'https://chargrilldavidson.com', 'http://tijuanatanaz.com/', 'http://scifest.vegas/contact/', 'http://www.davinciflowershop.com', '1592151608', 'http://www.eventsbyfirstrose.com', 'http://outremont.lapiazzetta.ca', 'http://www.eurowise.com', 'http://www.rocrace.com/charlotte', '1592151621', 'https://www.wellsfargo.com', None, None, 'http://www.powerhousegym.com/schedules-i-407.html', 'http://www.dogsbycindy.com', None, 'http://www.kngmg.com', '1592151643', 'http://www.odelaybagel.com/', 'http://www.harbsbarbershop.com', None, 'http://stevedavishtgac.com', 'https://www.lajoliefemme.ca', 'http://www.alphagraphics.com/centers/westlake-ohio-us649/index.html', 'http://www.hellofacepaint.com', None, None, None, 'https://www.southwestmobility.com', None, None, None, 'http://www.lbvgallery.com', None, 'http://www.pageplusaz.com', 'http://gimelconstruction.homestead.com', 'http://www.gelatostar.com', 'https://www.lawncontrolcenter.com', 'http://www.anotherstory.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.rnrcarpetcleaning.com', 'http://www.heistbrewery.com', 'http://www.sharkystaphouse.ca/', 'https://negretelawfirm.com', None, 'http://samsxpresscarwash.com/huntersville', None, 'http://www.righttime-inc.com', None, 'https://locations.monro.com/oh/cuyahoga-falls/1584-state-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.yclibrary.org/lakewyliebranchdetails.php', 'http://www.publix.com', 'https://locations.monro.com/oh/north-olmsted/4565-great-northern-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, None, None, 'http://tonysicecream.com', 'http://bigapplebagels.com/', 'http://www.clwplumbing.com/', 'http://fcautobody.com', None, 'http://restaurants.basspro.com/FishCompany/Mesa/Default.aspx', None, 'http://www.bk.com', 'http://www.dom.pitt.edu/id/About.html', 'http://vervewellnesscenter.com/', None, 'http://www.oliveoilaz.com', None, 'http://www.nevadadentalgroup.com/', None, 'http://www.castcadearizona.com', 'http://www.JimmyJohns.com', 'http://www.generationsmedcenter.com', None, 'https://www.circlek.com/store-locator/US/phoenix/4135-w-anthem-way/2709192?location=85086', None, 'http://lotusservicesaz.com', 'http://www.mysteryadventureslasvegas.com', 'http://www.swirlyz.ca', None, '1592151813', 'http://www.kfc.ca/store/sunrige-mall-101-2525-36-st-ne-calgary', 'http://www.torontocarwrap.com/', None, 'http://www.countyofdane.com/lwrd/parks/viking.aspx', 'http://www.golfpinehills.net', 'http://www.ddsdiscounts.com', 'http://www.gailambrosius.com/', 'http://wagntails702.wix.com/vegaspetgrooming', 'http://www.rawfitnesspersonaltraining.com', None, None, 'http://www.vedatakeout.com', None, 'http://www.cocinaelvis.com', 'http://www.filosophy.ca', None, 'https://www.interstatebatteries.com/locations/all-battery-center-las-vegas-nv', 'https://www.frysfood.com/storeHours?store=66000064', None, 'http://www.kitchenova.com', 'http://www.cosmiix.com', 'http://www.7-eleven.com/?yelp=29644', 'http://www.jasonsdeli.com/restaurants/az/glendale/glendale-deli', 'http://www.clevelandtallships.com', 'http://www.eathopscotch.com', 'http://www.RentMontereyApartments.com', 'https://stores.hallmark.com/nc/matthews/jansens-hallmark-shop-matthews-nc-23514.html', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'https://www.orthocarolina.com/locations/gastonia', 'http://www.phoenixsymphony.org', 'http://balletaz.org', 'http://www.PazanGallery.com', 'http://www.teaspaceus.com', 'https://www.nsm-seating.com/national-seating-mobility-relocates-phoenix-office/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.gotyoucoveredmusic.com', 'http://handelsicecream.com', 'http://www.babessportsbar.com/', 'http://www.thegreenmango.com', 'http://teamzrestaurant.com', 'https://www.chick-fil-a.com/stapleydrive', 'http://car-detailing-cleveland.com', '1592151935', None, 'http://www.a-zequipment.com', 'http://www.adventurecjd.com', 'https://ad.doubleclick.net/ddm/clk/434423236;236814625;d', 'http://www.hotrocksdiner.com/', 'http://www.studiowe.ca', 'http://www.floorcoveringfactoryoutlet.com/', 'http://www.nutrition51.com', 'https://www.hungryhowies.com/store/hungry-howies-01809?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=1809&utm_content=Website_Link', 'http://www.zbakeryandcafe.com', None, 'http://www.payless.com', 'http://www.onefinedayphotography.com', 'http://www.sherwin-williams.com/store-locator/paint-store/Phoenix/AZ/8160', 'http://www.acehardware.com/store-details/07473', 'http://www.lacakery.ca/', 'https://agents.farmers.com/nv/las-vegas/jason-suemoto?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://www.scpchiropractic.com', 'http://www.housepaintinginphoenix.com', 'http://www.autoaccessoriespgh.com', None, 'http://www.baskinrobbins.com', '1592151997', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.tcby.com', 'http://www.creativestonecrafters.com', 'http://www.cocosbakery.com/', 'http://www.salonjovon.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.babyramacanada.com', None, 'https://guardlocksmithgaragedoor.com/locksmith-garage-door-repair-scottsdale-az', 'http://www.rei.com', 'https://www.burnsidebarbecue.com', 'http://www.pizzeriaviamercanti.ca/', 'https://www.sprouts.com/stores/details/-/store-details/view/store/19/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.wilsonniblett.com', 'http://www.zoltons.com', None, 'http://www.hirtsflowers.com', None, 'http://www.badboy.ca/en/pg-storelocator-Mississauga', 'http://www.blm.gov/nv/st/en/fo/lvfo/blm_programs/blm_special_areas/red_rock_nca.html', None, 'https://www.pteglv.com/locations/pts-pub/rainbow-cheyenne/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://www.crabcrackernc.com', None, 'http://magiceric.com/', 'http://www.mathnasium.com/scottsdale', None, None, None, 'http://www.textilemuseum.ca/', 'http://www.tpcmadison.com', 'http://www.freshstartaz.com', '1592152094', None, None, 'http://pizza.dominos.ca/Calgary-Alberta-10108', 'https://techfourlife.com', None, 'http://www.ttroadhouse.com', 'https://www.walgreens.com/locator/walgreens-5975+weddington+rd-matthews-nc-28104/id=10255', None, 'https://www.walgreens.com/locator/walgreens-5400+pearl+rd-parma-oh-44129/id=3314', 'http://www.ryanfootandankleclinic.com', 'http://www.hansabrewery.com', 'http://gabbys.ca/locations/gabbys-kingston-road/', 'http://westcitysnackbar.com', 'http://www.litchfield-park.org/index.aspx?NID=288', 'https://www.petsuppliesplus.com/Store/OH/Parma/Parma/120?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.centralbarkusa.com/madison-southeast', 'http://www.mattress.org', None, 'http://www.hobbylobby.com/StoreDetail/500', None, 'http://www.hairandcosaloninc.com', 'http://www.dennys.ca', 'http://bangzartandhairsalon.com/', None, None, 'http://www.joeslakewoodcomputer.com', None, 'https://milios.com', 'http://www.thescottresort.com/?utm_medium=enhanced-profile&utm_source=yelp', None, 'http://meskeremincharlotte.com/', 'http://sergio-daae.squarespace.com', '1592152184', 'http://www.courtesydental.com', None, 'http://www.soma.com/store/home.jsp?cmp=MOC_yelp', 'http://www.paradisevalleyhomes-forsale.com', 'https://thelasvegaslounge.com', 'http://www.eandgrealestate.com', 'http://www.laundrybasketvillager.com/', 'http://www.marybekitchen.com', 'http://www.gelatospot.com', 'http://professornailsandspa.com', None, 'http://www.buttermilkfinewaffles.com', 'http://www.tubeaudio.com', 'http://jeffreyngmd.com', 'http://www.lenailsonline.com', 'http://www.gnc.com', None, 'http://www.9round.com/fitness/madison-wi', 'http://www.alltattoos.net', None, 'https://www.officedepot.com/storelocator/az/glendale/officemax-6171/', '1592152244', None, 'http://www.downtownphoenixrentals.com', None, 'http://www.strawberryhedgehog.com', None, 'https://azwestpainting.com', 'http://www.abundance-a.com', 'http://silvertoncasino.com/dining', None, None, 'http://www.nellisfamilyhousing.com/', 'http://www.theloftycupcake.com', 'http://impchandler.com', None, 'http://www.lassendas.com/Casual-Family-Dining-Sports-Bar-Happy-Hour-Mesa-The-Grille-Las-Sendas.html', 'http://www.edgewaterbarandgrille.com/', 'https://www.guardianmortgageonline.com/branch-managers/arizona_mortgage_branch_manager_steve-howard/', None, None, 'http://www.marketdistrict.com/Locations/Detail.aspx?LocationID=7', None, None, None, None, None, None, 'http://ingenuitycleveland.com/', 'http://www.lcbo.com', None, 'http://www.starbucks.com', 'http://www.marcellos.ca/', 'http://www.clevelandgaragedoors.net', 'http://www.africanabbqcurriesdrinks.com', 'http://www.pvbarbers.com', 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', 'http://www.PawsPetServicesInc.com', None, 'http://svdppitt.org/stores/store-locations-directions/', 'http://www.newliferoof.com', None, None, None, 'https://agents.farmers.com/az/carefree/jason-grifo?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://venturagrill.com/', 'http://www.libertyburgers.ca', 'http://www.mushkaki.com/', None, None, 'http://www.enchantress.com', 'http://www.belfilandscaping.com', '1592152383', None, None, None, None, 'http://www.rubymarie.com', None, 'https://locations.wendys.com/canada/on/mississauga/6966-financial-drive', 'http://www.dmvnv.com/', None, None, None, None, 'http://www.badattitude.com/', 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', 'http://www.ogreatcut.com', 'http://www.analoguegallery.com/', 'http://www.arizonadigestivecenter.com', 'http://www.murrysvillespa.com', 'http://www.bobstvaz.com/', None, 'https://www.rcpw.com', 'https://www.arizonatermitespecialists.com', 'http://www.familypetsalon.com', 'https://novasolutions.ca', 'https://www.kwiktrip.com/Locations/Details/673/', 'http://locations.harristeeter.com/nc/charlotte/205/', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_112', 'http://www.greenleafwholesale.com', None, 'https://nestnailwellness.com', 'http://www.lowes.com', 'http://www.soupersalad.com/', 'http://www.mammaspizza.com', 'http://www.sacredrootsaz.com', 'http://bk.com/', 'http://www.eldoradocasino.com', 'https://locations.wendys.com/united-states/wi/sun-prairie/743-w.-main-st.', 'https://salsalocamexicangrill.square.site', 'http://www.tph.ca/print/toronto-yonge-st-eglinton-ave', None, 'http://www.batteriesandgadgets.com/pages/contact_us', '1592152501', 'http://www.westthirddeli.com', 'http://www.charmeck.org/', None, 'https://growgeneration.com/?utm_source=yext', 'https://oldpinevillepremiumpub.com', None, None, None, 'http://www.swspineandsports.com', 'http://www.thepubat333.com', None, 'http://www.quiznos.com', 'http://www.autohausofnorthscottsdale.com/', 'http://www.deathinvenice.ca', 'https://sobamesa.com', 'https://wongs-chinesedining.com', None, 'http://www.megatunes.com', None, 'http://www.phoenixpaver.com', 'https://www.myplacehotels.com/my-place-hotel-north-las-vegas-nv', None, 'http://www.wehnergroup.com', 'http://liveatwynnpalms.com', None, 'http://www.artisanantiquescleveland.com', 'http://chaletvet.com', None, 'http://www.miasalonstudios.com', None, 'http://www.eatchinakitchen.com', 'http://www.williamsstainedglass.com', None, None, 'http://elcompatireshoplv.com', '1592152616', None, None, 'http://www.tbcmovers.com', 'http://www.residencesonfarmer.com/', 'https://jojosjerky.com', 'https://agents.allstate.com/mike-seifer-henderson-nv.html', 'http://www.domyresume.net', 'http://www.hongkongvintage.com/', 'http://www.newtowndds.com', 'http://www.chuparosapainting.com', 'http://ottavio.ca/contact-greenfield-park-rive-sud/', None, None, 'http://www.charmeck.org/', 'http://www.ae.com/web', 'https://www.loandepot.com/branches/Henderson-NV?sc_camp=DE925F8ECA0F4E0D8092C7E108A615A3', 'http://www.judonspainting.com', None, 'http://www.peoplesmortgage.com/loan-officer-team/broker/Tamiarmijo', None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.pinkhousenc.com/', 'http://www.kobootcamp.com', 'http://www.standa.ca', 'https://www.pepsolar.com', 'http://www.onenevada.org', 'http://623pc.com', None, None, 'http://www.expressionswaxspa.com/about-us.html', None, 'http://www.azburgershoppe.com', 'http://italianvillagepizza.com/', None, 'https://www.newportmotorslv.com', None, 'http://mandys.ca', None, 'http://www.joelcohenmd.com', '1592152774', None, 'https://www.walgreens.com/locator/walgreens-220+s+century+blvd-rantoul-il-61866/id=9965', 'http://topnotchnailsspa.com', None, 'http://www.passengerscafe.com/#hello', None, None, None, 'http://enginehouse.com', 'http://www.cartridgeworldphx.com', 'https://www.cellphonerepair.com/mayfield-heights-oh/', 'http://towingscottsdale.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.essentoronto.com/', 'http://avis.com', 'http://www.z-vw.com//?cs:pro=repman&cs:e=yelp', 'http://www.patriciacakes.com', 'http://www.acepoollv.com', None, None, 'http://www.firepatio.com', None, 'http://jerryrhynescollision.com/locations/pineville-location/', None, None, None, 'http://www.michaelkluthe.com', 'https://www.youfit.com/gym/phoenix-32nd-st-7406', 'http://www.woofgangbakery.com', 'http://www.azandersonanimalclinic.com', None, 'http://Phomono.ca', 'http://www.sunscreens-armadillo.com', None, 'http://www.donatos.com', None, 'http://www.noviamia.ca', 'http://www.paseodelpradoapts.com', None, 'http://www.redrockcanyonlv.org', 'http://Www.Tailsandbones.com', 'https://pawnscottsdale.com', None, None, 'https://www.waltsjewelers.com', None, 'http://www.oasishookahlv.com/hookahcatering.html', None, 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.ontrackdj.com', 'http://vintagelucys.com', None, 'http://www.regissalons.com/salondetail/default.asp?salonid=4818', 'http://www.DJEliteAZ.com', 'http://www.stadiumbargrill.com', 'http://kwcafeterias.biz', None, 'http://www.joycitytires.com', '1592152981', 'http://luckithaibistrolasvegas.justcafepages.site', 'http://www.thebakedbear.com', None, 'http://www.finewinereserve.com', 'http://scfapm.net/', 'http://www.shoppersdrugmart.ca', 'http://www.thrivehomeservice.com', 'http://www.atomiccomics.com', None, None, None, 'http://www.regenesisskinstudio.com/', 'https://www.searshomeservices.com/locations/appliance-repair/pa-pittsburgh/1000-robinson-center-dr', None, 'https://stores.jcpenney.com/pa/monroeville/salon-monroeville-pa-0199.html', None, 'http://www.cosmosrecords.ca', 'https://nothingbundtcakes.com/bakery/AZ/glendale?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=glendale_56', '1592153049', 'http://bentoburrito.ca/', 'http://www.bigming.ca', 'http://www.rolenbrothersfence.com', 'https://juliagrambo.com', 'http://www.automaxxon16th.com', 'http://www.flatlinegrinding.com', 'http://www.hopingfurahome.com', None, 'http://www.UrbanPranaYoga.com', 'http://www.aamfg.com', 'http://www.808smokes.com', '1592153093', 'http://restaurantlabelleprovince.com', None, None, None, 'http://www.winners.ca', 'https://www.mamabaers.com', None, None, 'http://www.risquelv.com/', None, None, None, 'https://www.KFYIadvertising.com', 'http://www.christieclinic.com', 'https://showerdoors.binswangerglass.com/nc/charlotte/?utm_source=yelp&utm_medium=social&utm_campaign=showerglass&utm_content=urllink', None, None, 'http://www.thaitouchkitchen.com/', 'http://www.bk.com', 'http://www.spinbikeshop.com', '1592153170', 'https://www.crawfordtransmission.com', 'http://www.simpleshuttle.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://www.dreamcarrentals.com/', '1592153188', 'http://www.coldstonecreamery.com', 'http://www.tonicpgh.com', 'http://www.hydroshieldphx.com', 'http://www.bk.com', 'https://wellingtonsofcalgary.com', 'https://store.vioc.com/nc/gastonia/2650-e-franklin-blvd-28052-BD0014', 'http://kimaznailspa.wix.com/kim-az-nails-and-spa', 'http://superstore.ca', 'http://www.kilkearysautobody.com', 'https://skinaddictstudio.com', None, None, None, 'http://autopricecanada.com', 'https://westvalleypawn.com', None, '1592153258', None, 'http://www.clevelandymca.org/branches/westpark', 'https://www.azcontainers.com', None, 'http://www.techspector.com', 'http://www.dunkindonuts.com', 'http://www.napoca.ca/', None, 'http://www.brownleejewelers.com', 'http://www.arbys.com', 'http://www.kearnsandco.co', None, None, 'http://www.tommulligan.com', 'http://www.vegaslimocoach.com', 'https://locations.sonicdrivein.com/nv/lasvegas/6301-w.-lake-mead-blvd..html', 'http://www.westhillvet.com/', 'http://www.mark-taylor.com/arizona/laguna/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.fourpeaks.com', None, None, 'https://www.carewithconfidence.com', 'https://elementsmassage.com/tempe', None, 'http://www.millscleaners.com', None, 'http://cluffmechanical.com', 'http://www.buenoburgeraz.com', 'https://www.cinemark.com/northern-ohio/cinemark-cuyahoga-falls-and-xd', None, 'https://www.pittsburghparks.org/schenley-park-cafe-visitor-center', 'http://www.rossocoffeeroasters.com', 'http://www.edgewalkcntower.ca/', 'http://www.dunkindonuts.com', None, '1592153386', 'http://www.shell.us/', '1592153393', 'http://www.tolmachoff-farms.com', 'https://crisp-pizza.com', 'http://www.comebuy2002.com.tw/', None, 'https://www.perfectpalmssalon.com', 'http://www.regionsbistro.com', 'http://advancedtherapeuticsmassage.com', 'http://www.davidofflv.com', 'http://www.kvegas.com', None, 'http://www.farnsworthrealty.com', 'http://blueagavemadison.com', None, None, 'https://howardair.com/showroom/', 'http://www.photographerjun.com', 'https://www.desertdryclean.com', 'http://workoutanytime.com/mint-hill', '1592153469', None, None, 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', 'http://www.merlenormanstudio.com/nv/las-vegas/mn-10293/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.divasalonspa.com/', None, 'http://www.alexandani.com/pittsburgh', 'http://www.antoniospizza.net', '1592153499', None, None, 'http://www.pittsburghsbestremodeling.com', 'https://cvam.com', None, None, None, 'http://www.magomindfulness.org', 'http://www.twolouiesmarket.com/', 'http://www.runningroom.com/hm/', 'http://www.gamestop.com', 'http://www.fabletics.com', 'http://captiverooms.com', None, 'http://ad.doubleclick.net/clk;266326037;92222803;c?http://www.24hourfitness.com/FindClubDetail.do?clubid=205&edit=null&semiPromoCode=null&cm_mmc=Yelp-_-ClubPage-_-BusinessListing-_-Link', None, 'http://www.7-eleven.com/?yelp=19726', '1592153554', None, 'https://www.kalonsandglidewell.com', 'https://roiproperties.com', 'https://www.truenorthmortgage.ca/?utm_source=Yelp&utm_medium=yelp-ads&utm_campaign=yelp-ont', None, 'http://www.scottsdaleautogroup.com', None, None, 'http://www.papamurphys.com', '1592153591', 'http://www.beneficial-insurance.com', None, 'http://katespade.com', 'http://www.purelifehomeopathy.com', 'https://www.nhrandolphobgyn.org/locations--hours/charlotte.aspx', None, None, 'http://www.olgaallenhairsalon.com', 'http://www.cabowabocantina.com/vegas/', 'https://apricotlaneboutique.com/store/champaign/', 'https://locations.noodles.com/wi/fitchburg/2981-triverton-pike-dr--at-mckee-rd.html', 'http://clickserve.dartsearch.net/link/click?lid=43700044282974602&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.tlchudson.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'http://www.gmgbarbershop.com', 'https://communitytirepros.com/tires-auto-repair-6-phoenix-az', 'http://www.calgary.ca/CSPS/Recreation/Pages/Athletic-parks/Glenmore-Athletic-Park.aspx', None, 'http://www.2dadsbouncehouses.com', 'http://www.INTLscottsdale.com/', 'http://www.xingfutang.ca', 'http://www.thelashandsugarcompany.com', None, 'https://stores.hallmark.com/nc/pineville/amys-hallmark-shop-pineville-nc-38803.html', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEAA', None, 'https://www.azmonsterair.com', 'http://knockout-fitness.com/locations/gilbert/', None, None, None, None, None, None, '1592153709', None, '1592153714', 'https://vercini.com/stores/vercini-miracle-mile-shops-las-vegas/', 'http://signaturegalleries.com/ACs_Wyland_Signature.html', None, None, None, 'http://marsiglianospizzeria.com', 'http://www.byashleymarie.com', 'http://www.dominos.com', None, None, None, 'https://www.americasbest.com/store-list/pineville-la-71360/', None, None, 'http://www.kbbicycleshop.com', 'http://mastertune.ca', None, None, 'http://www.stevesknows.com', 'http://www.shopplanetblue.com', 'http://www.89002realtor.com', 'http://www.peoplesutility.com', 'http://www.silverstatecu.com', 'http://www.crossfitmagna.com', 'https://www.olivegarden.com/locations/ab/calgary/calgary-northgate-plaza/4345?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:calgary-ab-4345_pl:locurl_rd:1743', 'http://dishosteria.com', 'http://gcbc.gcu.edu', None, 'http://www.bluewaterimaging.ca/', 'https://bikedepot.com/stores/toronto/', 'http://angelosgilbertbarbershop.com', 'http://www.teacoffee.com', 'https://locations.usbank.com/index/arizona/phoenix/west-bell-rd-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.nevadacoinmart.com', 'http://www.cupcakes-canada.ca', 'http://www.mastertoddy.com/', 'http://www.venetian.com/restaurants/italian/tintoretto-restaurant-bakery.html', None, 'http://www.videoproductionscottsdale.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/PHXEL', 'http://www.wineandspiritfestival.ca', 'https://www.supercuts.com/locations/ca/oakland/rockridge-district-haircuts-8050.html', 'http://www.cvlt.org', 'http://www.9round.com/fitness/madison-wi', 'http://hobakkoreanbbq.com', 'https://beavertails.com/shops/', 'http://friendsofdormontpool.org/pool.html', 'http://www.applyapprovedauto.com', None, 'http://www.customdentures.us', 'http://www.partysavvy.com', 'http://www.oliverannie.com', 'http://abrazodiabetes.com', 'http://www.i9sports.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://www.dunkindonuts.com', 'http://www.crossfitcholla.com', 'http://HairMajesty.mysalononline.com', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://vespucciconsignment.com', 'http://www.dominos.com', 'http://www.hangoverbail.com', 'http://www.harmonybarandgrill.com', 'http://LiveAtArtessa.com', '1592153958', 'http://drkaylaeckart.com', None, 'https://www.va.gov', 'http://www.starbucks.com/store/9334/', 'http://thesweatlab.com', None, None, None, 'http://www.homesense.ca', None, 'http://www.dominos.com', None, 'http://www.zerorezpgh.com', None, None, 'http://whasn.com/locations/whasn-henderson/', '1592154010', 'https://haircutmenraintreeranchchandleraz.com', 'http://themonticello.com', 'http://www.seagullbook.com/', None, 'https://www.publicstorage.com/arizona/self-storage-mesa-az/85210-self-storage/787?pid=wyelp&CID=1245&CHID=AFL', 'http://protecrepair.biz/', 'https://www.vapeloft.com/vaughan-vape-shop', 'http://www.futons-4-less.com/', 'http://www.unitedcabcle.com', 'http://www.pinkladiesmaids.com/', None, None, 'http://www.heroburgers.com', 'http://www.coinlesslaundry.com', 'http://www.mortgageandcreditpro.com', None, None, 'http://www.caesarspalace.com', 'https://www.gohealthuc.com/north-carolina/charlotte/quail-hollow?utm_source=yelp&utm_medium=referral&utm_campaign=yelp%7Clistings%7C2020-nc-null-novant-011520-quail-hollow', None, '1592154093', None, 'http://www.akanails.com', None, 'http://doorfiftyfive.com/', 'http://opasouvlaki.ca?utm_source=yelp&utm_medium=website-click&utm_campaign=enhanced-profiles', 'http://northamericanspine.com/', 'http://www.nutrishopcharlotte.com/', None, 'http://www.plazaappliancemart.com', None, None, 'http://www.chickrotisseriebar.com', None, 'http://www.losolivosrestaurants.com', None, None, None, 'www.rustycage.ca', None, 'http://www.newcityphx.com/', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.pnponecarecleaning.net/', 'http://ronsserviceandtire.com', 'https://simonmed.com', 'http://www.streetsaw.com', '1592154185', '1592154189', 'https://bosshairsalon.com', '1592154198', 'http://www.speedydetail.ca', 'http://www.dentalspalv.com', None, 'http://www.taketimetorelax.com', None, 'http://www.lvcmc.com', 'http://www.fkaiser.com', None, 'http://www.vinorossorestaurant.com', None, 'http://www.dwellstudentmadison505.com', None, 'http://www.DornHardware.com', None, 'https://www.atmosphere.ca/stores/calgary.html', 'http://anvilbaraz.com', 'http://thetreeguylv.com', None, 'http://www.redrockcanyonlv.org', 'http://www.chachis.ca', 'http://www.decadenceculinary.com', None, 'https://www.sierracanyonaz.com', '1592154281', 'https://providenceeye.com', 'https://locations.sonicdrivein.com/il/savoy/101-calvin-street.html', 'https://cosmomusic.ca', '1592154349', 'http://www.banfield.com/veterinarians/az/phoenix/pho?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.desertspringsrealty.com', 'https://www.valuecityfurniture.com/store-locator/pa/pittsburgh/451-clairton-blvd', 'https://www.speedy.com/shops/newmarket/en/', 'https://stores.anntaylor.com/factory/us/nv/las-vegas/7400-las-vegas-blvd-south.html', 'http://splashwindowcleaning.com', None, 'http://incascuisine.com', 'http://kierlanddentalcenter.com/', 'http://www.cherrystbbq.com', 'http://www.hznvet.com/', 'https://www.enterprise.com/en/car-rental/locations/us/oh/chardon-3928.html?mcid=iyp:8368400', 'http://www.gansercompany.com', 'http://casaritasmexicangrill.com', None, 'https://www.theelementlv.com', 'http://www.olde8automotive.com', 'https://www.241pizza.com', 'http://kindmedsaz.com', None, None, 'http://www.blimpcitybikeandhike.com', None, None, 'http://www.championfenceinc.com', None, 'https://www.anytimefitness.com/gyms/3397/Montreal-QC-H2W-1Y7/?utm_source=yelp&utm_medium=local', '1592154453', 'http://www.enchantedvalleyacres.com/', 'http://furbabiesresort.com', None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=586&utm_content=bpas', 'http://www.visualcreations.vegas', 'http://www.phoenixazhomes4u.com/', '1592154476', '1592154480', 'http://www.phoenixmedicalgroup.com', 'http://www.azvpcp.com', 'https://www.petsmart.com/stores/us/nv/las-vegas-store1153.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'https://www.sellitquickhs.com', 'http://a1carpetmasters.com/', None, 'http://www.arcoflifechiro.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, 'http://www.sears.com/stores/north-carolina/monroe/0002008.html', 'http://www.EliteBartend.com', 'http://www.adriaticflooring.com', 'http://www.BombHairVegas.com', 'https://www.sonoraquest.com/find-a-location/sun-lakes-alma-school-riggs/', None, 'https://www.bluebreeze216.com', 'http://www.swgeneral.com', 'http://www.wetpetsandfriends.com', 'http://www.dirkcpa.com', 'http://www.alivedanceworks.com', 'http://www.coldstonecreamery.com/stores/20181?latitude=33.6071829&longitude=-111.9403254', 'http://www.silhouettebridallv.com', 'http://www.alibabas.ca/index.php?route=common%2Flocation_details&loc_id=12', 'http://www.jakesbarvegas.com/', None, 'http://www.sav-onplumbing.com?srccode=yelp_track', None, 'http://www.edelmanplumbing.com', 'http://www.starbucks.com/store/11823/', 'http://www.scentair.com', None, 'https://www.ihop.com/en/restaurants-south-las-vegas-nv/7490-s-las-vegas-blvd-3096', None, 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/mississauga-(2).aspx', 'http://www.aspirekidsports.com', 'http://www.bloodbrothersbrewing.com', 'http://www.sherwin-williams.com/store-locator/paint-store/Gilbert/AZ/8286', 'http://www.blackeagletoronto.com/', 'http://www.maderacabinets.com', 'http://www.citycleaner.com', 'http://todaysinteriors.com/', 'http://4seasonslandscapinglv.com', None, None, 'http://ashleynailsspachandler.com', None, 'https://www.walmart.com/store/1646/mesa-az/details', 'http://www.daphnesbakery.com', 'http://www.vynepowdercoating.com/', '1592154609', 'http://www.cityfresh.org', None, None, 'http://www.crystalsatcitycenter.com', None, None, 'http://www.accountingprose.com/accountingprose-arizona/', 'https://order.pizzapatron.com/menu/phoenix-indian-school-road?utm_source=Yelp&utm_medium=Order&utm_campaign=Ordering', None, 'http://www.beachesbrewing.com', 'http://www.robertocarpetclean.com', 'http://skyharbor.com', 'http://www.brodywebdesign.com', None, '1592154648', None, None, 'http://www.puckettsfarm.com', 'http://www.bishopsplum.com', 'http://www.alleen.com', 'https://www.hilton.com/en/hotels/clemehx-hampton-suites-cleveland-mentor/?SEO_id=YELP-HP-CLEMEHX', 'http://www.ariatroofing.com/', 'http://yazlounge.com', 'http://www.safaripetcenter.com', 'http://www.sukhothaibistro.com/', 'http://teavana.com/ca', 'http://www.furniturestopaz.com/', 'http://www.apexoutdoortreeservices.com', 'http://meridianlv.com', None, None, 'http://www.eddys.com', 'http://www.bobscopyshop1.com', '1592154699', 'http://www.kingspointsmallengine.ca', 'http://www.elpolloloco.com/locations/store/5541', 'http://www.skinstudioaz.com/', None, None, 'http://www.liquordepot.ca/?utm_source=Yelp&utm_medium=Online_Listings&utm_content=Location&utm_campaign=LiquorDepot_AB_Q3_July_September_2017', 'http://www.hcdentallv.com', 'http://www.tomduffyinsurance.com', None, 'https://www.chandleraz.gov/explore/chandler-aquatics/centers-and-pools/folley-pool', 'https://jessieleephotos.com', 'http://Www.crawlingsquidtattoo.com', 'http://www.bojangles.com', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.airportlimocanada.com', '1592154747', 'http://www.wellsfargohistory.com/museums/phoenix', None, 'https://www.xtremevapour.com', '1592154760', 'http://sunvalleynailspa.com/', 'http://www.quantumcollections.com', None, None, 'http://www.grandstayhospitality.com/find-a-hotel/locations/mount-horeb/overview', 'http://www.swingpt.com', 'https://certapro.com/summerlin/?utm_source=YextNetwork&utm_medium=organic&utm_campaign=YextNetwork', None, 'http://biggscamera.com', 'http://www.deekerssidetracks.com/', 'http://www.humblewinebar.com', 'http://www.theofficepub.ca', 'http://hhtattoo.com', 'http://www.blackphoto.com', None, 'http://kakaallyoucaneat.com', 'http://www.restartbar.com', None, None, 'http://kiplinautorepair.com/', 'http://www.thepizzacompany.biz', 'http://www.checkeredmoon.com', '1592154823', 'http://www.michaelpwebbersondds.com', None, 'http://www.potbelly.com/MayfieldHeights', 'https://www.walgreens.com/locator/walgreens-2363+s+lindsay+rd-gilbert-az-85295/id=5215', '1592154837', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://www.kirchappliance.com/', 'https://www.erinparktoyota.com', 'http://www.parkatdeervalley.com', 'http://www.westgateaz.com', 'http://www.sugo.ca', None, 'http://bellacinos.com', None, 'http://mintstrength.com', 'http://www.napolivince.ca', 'https://parsleymediterranean.com', 'http://sweeteezsweets.com', 'http://www.pspohio.com/', 'http://www.readytuxedo.com', 'http://www.wildchildclothes.com', 'http://www.mexicanbowl.ca', 'https://bostonpizza.com/en/locations/sunridge.html', None, 'https://www1.shoppersdrugmart.ca', 'http://www.baskinrobbins.com', None, 'https://www.long-mcquade.com/location/Ontario/Brampton', '1592154901', 'http://www.uhhospitals.org/westlake/urgent-care', 'http://www.wholehomeinspectionsllc.com', 'http://www.beautif-eyestudios.com', None, 'http://allbritematerials.com', 'http://www.victoriassecret.com', 'http://www.fransrestaurant.com', 'http://www.fandoctor.com', 'https://www.popeyes.com/store-locator/store/restaurant_83325', 'https://www.usstoragecenters.com/self-storage/arizona/glendale/us-storage-centers/126', 'https://stores.nordstromrack.com/us/az/gilbert/2090-e-williams-field-road?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=154&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', 'http://www.trilogylife.com/communities/arizona/vistancia/', 'http://www.carmellaspizza.com/', 'http://www.skysongcenter.com', 'http://www.sessomsandsons.com', 'http://fossilandhaggis.com/', None, None, 'http://casablancanails.com', None, 'http://www.erbertandgerberts.com/locations/detail/sun-prairie', 'https://cafevialinda.com', 'http://www.tesororanchapts.com', 'http://www.icecreampizzaworks.com', 'http://www.pizzanova.com', 'http://www.te-koop.ca', None, 'http://www.cardealsdirect.ca', 'http://getnutslab.com', 'http://www.artinthepark.org/', None, None, None, 'http://www.CampanasPizza.com', None, None, 'http://www.phoenix.gov', 'http://www.pwaesthetics.com', None, 'https://www.encantopoolcare.com', None, None, 'http://greekstop.ca', 'http://www.mortproductions.com', 'http://trendsettereyewear.com', 'http://www.starbucks.com/store/15887/', None, 'https://www.anytimefitness.com/gyms/4028/Mint-Hill-NC-28227/?utm_source=yelp&utm_medium=local', 'https://www.gowireless.com/stores/az/goodyear/goodyear-estrella-marketplace/', 'http://www.kitchenstuffplus.com', None, 'https://www.choicehotels.com/CN283?mc=blypypaf', 'http://phxfloors.com', 'http://www.tenpennyimc.com', 'http://www.winchellspub.com/', None, None, 'http://www.kisellasurgery.com', 'http://www.thegraniteshopofmadison.com', 'http://www.coffeebean.com', 'http://www.completeeyecareaz.com/', 'http://www.palazzo.com/azure', 'http://www.azinspector.com/', 'http://www.dollartree.com/home.jsp', None, 'http://www.cartersgymnastics.org/', None, 'https://www.extraburger.ca', 'http://www.elhefe.com/scottsdale', 'http://www.baschs.com', None, 'http://www.monroevillekia.com', 'http://farmersfurniture.com/', None, None, 'http://www.abestautorepair.com', 'http://www.northlakechiro.com', 'http://drkennedychiro.com/', 'http://www.artgalleryofmississauga.com/index.html', 'http://www.uptowncharlottecleaner.com', 'http://www.buckdeitzphotography.com', 'http://www.manuelsaz.com/', 'http://www.funkymunky.ca', 'http://tandmautomotive-hub.com', 'http://smokespoutinerie.com', 'http://www.galleriashoppingcentre.ca', 'http://www.functionpilates.com', None, '1592155146', 'http://www.allthingseyeslv.com', None, None, None, 'https://www.mgmgrand.com/en/nightlife.html', 'https://arizona.weidner.com/apartments/az/phoenix/arezzo/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.flawlessfaceandfigure.com/', '1592155164', 'http://www.clerkofcourt.maricopa.gov/', 'http://www.chaska.ca/', 'http://www.highdesertoralsurgery.com', 'http://www.wins.doitbest.com', 'http://www.gtmassages.com', 'https://www.pioneerfamilypools.ca/locations/newmarket/', None, 'https://www.lvspaandnailsvegas.com', 'http://thebikeproject.org', 'http://www.850Degrees.ca', 'https://stores.joann.com/oh/hudson/171/', None, 'http://www.phoenixlockoutsandroadsideassistance.com', 'http://www.bettercontracting.ca', 'https://www.popeyes.com', None, None, 'http://icirides.com/', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.ritascleaningllc.com', None, '1592155224', 'http://www.rockbottom.com/', 'https://soswaxlv.com', None, 'http://www.pelicanssnoballs.com/lakewylie123.php', 'http://www.shopmetcalfes.com', None, None, 'https://www.themotherhoodco.com', None, 'https://losgirasoles.us', None, 'http://www.bowlofgreensfinesalads.com', None, 'http://planetpetopia.com', 'http://www.platinumentourage.com', 'http://www.drsteed.com', None, 'http://www.chopchopwok.com/', 'http://www.mizumisushi.ca', None, 'http://www.lachotsmiles.com', 'http://www.laketowne.com', 'http://www.carolynes.com', 'http://www.golfsmith.com', 'http://www.themerchant.biz', None, 'https://thepetclub.com', 'https://www.loszarapes.com', 'http://www.dmvnv.com/locat.htm', 'http://www.mrpuffs.com/fr/', None, 'http://distilledbeautybar.com', 'http://www.intothefirepizza.com', 'http://www.womeninneed.net/', 'http://www.rianahairstudio.com', 'http://planetsmoothie.com/', 'http://www.asianhealingartsandacupuncture.com/', 'http://www.sosappliancerepair.com', 'http://www.greaterlasvegasdental.com', None, None, 'https://www.cellphonerepair.com/phoenix-central-az/', 'http://GreenMaid.Info', 'http://www.goldennugget.com/home/entertainment_attractions/defending_the_caveman/', 'http://www.vegasvacuumsewing.com', None, 'http://www.rockwoodnaturalmedicine.com/', 'http://www.club42.com', 'http://newmarket.colmustardspub.com', 'http://www.lazyloafandkettle.com', None, None, 'http://www.thepilatesbodylasvegas.com', None, None, None, 'http://www.laptopxchange.com/phoenix-az-computer-repair/', 'https://www.4pawspetresort.com/?utm_source=yelp&utm_medium=social', 'https://www.cartridgeworld.com/las-vegas-nv/89102-0318/about-us', None, None, 'http://www.economy-glass.com', 'http://www.novaristorante.ca', None, None, 'http://locations.harristeeter.com/nc/davidson/268/', 'https://dentalsolutionslv.com', 'http://www.doggiedoorsontherun.com/', 'http://www.thaicuisineexperts.com', 'http://www.aztechglasstint.com', None, None, 'http://www.designercakeshop.com', 'http://www.myfoodcity.com', 'http://www.kmart.com/stores/michigan/monroe/4098.html', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'https://www.themetatfashioncenter.com/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.mcqueenplumbing.com/index.html', None, 'http://communityculinary.org/', 'http://www.classroomcentral.org', None, 'http://www.saltydogpetspa.net', 'http://www.thebodyrx.com', None, 'https://www.moonvalleynurseries.com/services/tree-service?utm_campaign=yelp&utm_source=yelp-az&utm_medium=tree-care', 'http://www.wm.com/', '1592155455', 'https://dema.az.gov/army-national-guard/papago-park/arizona-military-museum', 'http://www.glendalesalonaz.com', 'http://www.hcpnv.com/clinic/wynn', 'http://www.noirtraining.com', 'http://www.heritagecrownaz.com', 'http://massageworkscharlotte.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=803&utm_content=bpas', 'http://www.OrganicMassageCleveland.com', 'http://www.BeefOBradys.com', '1592155482', 'http://www.parktowerapts.com', 'http://chartiersanimalhospital.com/', 'http://ordercasadeplata.com', 'https://www.omniwellnesscenter.com', None, None, 'http://www.horsinaround.ca/', 'https://petvalu.com/location/2034', None, None, 'http://www.karlaskarslv.com/', 'http://www.dogsuppliesvegas.com', 'http://www.savon.com', 'http://www.foodbasics.ca', 'http://www.cryscakecreations.com/', 'https://www.autorepairpittsburghpa.com', 'https://vrplayin.ca', None, 'http://www.philsebastian.com', 'http://www.gvdentalcenter.com/', 'http://www.barringtonplaceapts.com/', 'https://locations.theupsstore.com/az/surprise/15508-w-bell-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.hinkleyslighting.com', 'http://laptopexpert.com', 'http://www.bathandbodyworks.com', 'http://www.jimmysnycpizzeria.com', 'https://locations.theupsstore.com/az/phoenix/4802-e-ray-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.rotaryevolution.net/', None, None, 'http://www.baskinrobbins.com', 'http://www.apple.com/fashionshow', 'http://www.gohunanofstow.com', None, 'http://www.piacere.ca', None, 'http://www.azcenturypoolplastering.com', 'http://www.acclivityhealthcare.com', None, None, 'http://www.gallaghersexpertautorepair.com', 'http://www.containerbaryyc.com', None, None, 'https://www.superstitiongrandantiquemall.com', None, None, 'https://beehiveceilings.com', 'http://www.toppackgear.com', None, 'https://www.medexpress.com/location/pa/pleasant-hills/plp/?utm_source=yelp&utm_medium=paidsocial&utm_campaign=Evergreen', None, None, None, 'http://www.phoenixgreyhoundpark.com', None, '1592155627', 'http://www.autobell.com', 'http://slshotels.com/lasvegas/', None, None, 'https://www.hilton.com/en/hotels/pitsmes-embassy-suites-pittsburgh-downtown/?SEO_id=YELP-ES-PITSMES', 'http://bestchinainc.com', None, '1592155648', None, 'http://www.ArrowAH.com', None, 'http://dswcenter.com', None, '1592155660', None, 'https://tonyspokerschool.com', 'http://www.aetna.com', 'http://www.pizzafire.com', 'http://www.cakesonthemove.com', 'http://www.mandeljcc.org/', 'http://www.shakesandfranks.com', 'http://www.erindaleanimalclinic.com/', None, 'http://www.bloorwestvet.com', None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/501/?utm_source=yelp&utm_medium=listing&utm_campaign=website', None, 'http://www.bestmatt.com/', 'https://agents.allstate.com/wes-cain-gilbert-az1.html', None, 'http://www.scoutandcash.com', None, 'https://soccerpostarrowhead.com', 'http://www.saeedsbarandgrill.com', None, None, 'http://www.thesuntanboutique.com', None, None, 'http://www.childrensurgentcare.com', None, 'http://www.nikospizzalasvegas.com', None, None, 'https://enjoi-nails-salon.business.site', None, None, 'http://poolpartsplus.net/', None, None, 'https://locations.davidstea.com/on-toronto-1', 'http://clickserve.dartsearch.net/link/click?lid=43700006435127445&ds_s_kwgid=58700000444950505&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://myamericanfurnituregalleries.com', 'https://www.circlek.com/store-locator/us/peoria/9476-w-olive-ave/2706468', 'http://www.tikiicevegas.com', None, None, '1592155772', 'https://www.challengerschool.com/campus/nevada/las-vegas/silverado', None, 'http://www.fredmeyerjewelers.com', 'https://shadysidehousecleaning.com', None, 'http://serranosaz.com', 'http://www.expressflooring.com', None, 'http://www.clarkcountynv.gov/depts/clerk/services/pages/civilmarriages.aspx', 'http://griegofamilyeyecare.com', None, 'http://www.thunderbirdobgyn.com', 'http://www.bowkerchiropractic.com/', 'https://www.ventospizzapgh.com', 'http://www.minhchauoptical.com', None, 'http://www.michael-a-anderson.com', 'http://www.thewallpapermarketofmesa.com/', 'https://www.lvac.com/locations/henderson', 'http://subway.com/', 'http://www.sarphx.com', 'http://rokvegasnightclub.com', None, 'http://www.dovespa.ca', 'http://www.reprodux.com/', None, 'http://www.birch-dan.ca', 'http://www.nellosauto.com/', 'https://fantasticworldscomics.com', None, 'https://arizonadental.com/contact/phoenix-az-office/', None, 'http://www.strongsvillevacuum.net', 'http://www.ufixitautomotive.com', 'http://www.greenlinehair.com', 'https://www.lifestorage.com/storage-units/arizona/phoenix/85255/787-near-pinnacle-peak/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-AZ-787&utm_content=website-link&howheard=IYE', 'http://www.fremontweddingchapel.com', 'http://eh25.com/tasting-room/', 'http://www.paramountfinefoods.com', None, 'http://www.stevenjosephphotography.com/reviews', 'http://www.trappedcle.com', None, 'http://roxannesonline.com/', None, 'https://www.medusacle.com', None, None, 'http://www.fikesnet.com', 'http://cobraplumbing.net', 'http://www.tranteam.com', 'http://chinaaaadelivery.com', 'http://www.gangnamstreetlv.com', None, None, None, None, None, None, 'http://www.rapidrehablv.com/', '1592155928', 'https://reviveptandwellness.com', 'http://www.bronzebeautyst.com/', 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'http://www.dunkindonuts.com', 'http://www.savers.com', 'http://www.kulinars.net', None, None, 'https://www.tesla.com/findus/location/store/calgary', 'http://www.vibebeautylounge.com', None, 'http://www.sunsetstation.com/entertainment', '1592155959', 'https://www.moneytreeinc.com/branch/north-nellis', 'http://refinedlandscaping.com/', 'http://www.enterprise.com', 'http://www.kidsrkidsmatthews.com', None, None, 'http://www.simsroofingandsiding.com', 'http://www.shoplostfound.com/', 'http://www.galaxylg.com', 'https://www.chopsticksngrill.com', None, None, 'http://www.cal-am.com/communities/tropicana-palms', 'http://www.johnsfamilyrestaurant.com', 'https://www.toronto.ca/data/parks/prd/facilities/complex/337/index.html', 'http://www.onehazelton.com/', 'http://www.handinhandpreschool.com/index.html', 'https://diminishedvaluecheck.com', None, 'http://www.BradyLuxury.com', None, 'http://www.bikramyogamesa.com', 'http://www.niceguystechnology.com', '1592156015', None, 'https://www.kohls.com/stores/oh/macedonia-235.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.castlemegastore.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=phoenix_yelp&utm_content=2017', None, 'http://www.kingwongchinese.com', 'http://l.macys.com/scottsdale-az?cm_mmc=Yelp_Stores-_-Scottsdale-_-n-_-450&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Scottsdale_450&m_ac=yelp_stores&m_ag=n', 'http://www.therisingsun.ca/', 'https://www.ahn.org/locations/healthwellness-pavilion/peters-township', None, 'https://www.impactarcherylv.com', None, None, None, 'http://www.greatclips.com/', None, None, 'https://www.rossoutdoors.com', 'http://www.allianceurgentcare.com', None, None, None, 'https://bounceu.com/matthews-nc', 'http://www.thestudiosalon.biz/', 'http://www.jackieo.ca', None, 'http://www.owlremodeling.com', 'http://wiglewhiskey.com', None, None, None, 'https://store.vioc.com/nc/denver/7575-highway-73-28037-GM0004', None, 'http://www.mymindseyerecords.com', None, None, None, None, 'https://www.themovingmasters.com', 'http://www.rodgunandbarbers.com', 'https://locations.davidstea.com/on-toronto-1', 'http://scottsdaleautoglass.com', None, 'http://ad.doubleclick.net/ddm/clk/283420830;110240480;l', None, 'http://prestigebeautysalo.wix.com/prestigesalon', 'https://www.tileshop.com/store-locator/north+charlotte.do', 'http://www.colkerjanitorial.com/', 'http://www.justforpleasurenc.com/just-for-pleasure-2-north-charlotte-nc/', None, 'https://www.accucaredental.com', 'http://www.eltororestaurante.com', 'https://www.dicksspeedotach.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://trunzosauto.com', 'https://www.originaljoes.ca', '1592156149', 'http://RalphieMayVegas.com', None, 'http://www.greengrotto.ca', None, 'http://carolinashomestone.com', 'https://www.montecarloinns.com/markham-suites', 'https://www.wellsfargo.com', 'https://www.marathonpetroleum.com', 'http://www.recordsreduction.com', 'https://www.rmcf.com/AZ/Tempe50423', '1592156173', None, 'http://www.newcenturyhairdesign.com', 'http://www.bloorwestwinery.com', 'http://www.costco.com/warehouse-locations/scottsdale-az-427.html', 'http://thearomatherapygarden.com', 'http://www.aaronlending.com', 'https://local.biglots.com/nv/las-vegas/4500?zcp=pd_local_yelp', '1592156193', None, 'http://nes-electrical-services.business.site', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2faz%2fphoenix%2fmesa-west&sisearchengine=1524&siproduct=BEMES_Bus', 'http://othermamalv.com', 'http://www.n15salon.com', 'http://www.eastmesapediatrics.com/Home_Page.php', 'http://www.timhortons.com', 'http://www.shoelessjoes.ca', 'http://www.85254.com', 'http://www.funasiancuisine.com', None, 'http://mazzagarden.com/', 'http://www.littlecaesars.com/Locations/tabid/92/location/28079/Default.aspx?id=MTU1MzAwMTc%3d', 'http://www.accesstohealthcare.org', 'https://www.kidsquest.com/location/redrock/', 'http://www.siegelandcompany.com', 'http://www.miraclesofphoenixfitness.com', None, 'https://www.sheetz.com', 'http://www.elysianatstrose.com/', 'http://Www.federalgalley.org/restaurants/Shaka/', 'http://www.bowiechiropractic.com', 'https://www.topnotchwrapslv.com', 'http://simplicitysalonlv.com/', 'http://www.resumesolutions.ca', 'http://www.steamwayservices.com', None, None, 'https://collegehunkshaulingjunk.com?utm_source=yelp&utm_medium=organic', 'https://www.italianrestaurantrivergate.com', 'https://www.booksamillion.com', 'http://www.starskycanada.com/aboutus.php?s=4', 'http://www.platinumwellness.net', None, None, None, 'http://www.sheratoncavaliercalgary.com/calgary-restaurant', 'http://www.massagealacarter.com/', 'http://www.vintagewireandsupply.com', 'http://www.meyersmanagement.com', 'https://www.orthoarizona.org/physicians/Caleb-Behrend', 'https://heartlandfarmsanctuary.org', 'http://benefitcosmetics.com', 'http://stores.sportsauthority.com/az/phoenix/sporting-goods-phoenix-692.html', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd', 'http://www.thespiritconnection.com', None, 'http://Adventurehelicoptertours.com', None, 'http://www.studiowish.com', 'http://www.luckybrand.com', 'http://www.glamorgananimalclinic.com', 'http://evermorenevermore.com', 'http://www.flooring2day.com', 'http://www.rosedrivingschool.com', None, 'https://www.marquiscompanies.com/facility/marquis-centennial-hills/', 'https://www.queenofheartscasinoparties.com', 'https://store.vioc.com/wi/stoughton/1108-us-51-138-53589-GR0034', 'http://solylunabeautystudio.com', None, 'http://chinatocleveland.com', 'http://www.coffeedaklak.com', 'https://www.ediblearrangements.com/fruit-arrangements?utm_campaign=StoreID561&utm_medium=Listing&utm_source=Yelp', 'http://www.christophier.com', 'http://www.paramountfinefoods.com', None, 'http://www.ballantynevillage.com', 'https://stores.advanceautoparts.com/nc/charlotte/2910-freedom-drive?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', 'https://www.walgreens.com/locator/walgreens-6649+morrison+blvd-charlotte-nc-28211/id=1376', 'http://andysmechanicalser.mechanicnet.com', None, 'http://www.mattressfirm.com/', None, None, 'https://www.sandmanhotels.ca/hotels/calgary-airport/', 'http://www.MontysFurniture.com', 'http://www.urbanamarket.org', 'https://roadside-picnic.business.site', 'https://www.woolfeyecare.net', 'http://www.neatedupey.com', 'http://www.azpluscleaning.com', 'http://www.JimmyJohns.com', None, 'http://www.doubletreeinspectionsofaz.com', None, None, 'http://www.habitburger.com', None, 'http://www.ShaolinArizona.com', 'http://www.providencecourtapts.net', None, 'http://howardstowingpittsburgh.com/', 'http://www.fantasticsams.com/', None, None, 'http://www.contessacatering.com', 'http://projectmanagementacademy.net/las-vegas/pmp-certification.php', 'http://www.scottsdalelibrary.org/', 'http://richtreenaturalmarket.com/', 'http://www.heightslibrary.org/', 'http://www.alibabas.ca/index.php?route=common%2Flocation_details&loc_id=1', 'http://www.lids.com', 'http://www.terracharlotte.com', 'http://l.macys.com/chandler-az?cm_mmc=Yelp_Stores-_-Chandler-_-n-_-453&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Chandler_453&m_ac=yelp_stores&m_ag=n', 'http://www.galleriaatsunset.com', None, 'http://www.primrosegilbertsantan.com?utm_campaign=localmaps&utm_medium=maplistings&utm_source=yelp', 'http://www.glendalebarber.com', 'http://www.costnerlaw.com', 'http://www.permanentbeautyusa.com', 'http://www.scottsdaleaz.gov/Parks/chap.asp', 'http://www.picknsave.com', None, 'http://freshandeasy.com', None, None, 'https://www.teslamotors.com/en_GB/findus/location/store/rosspark', 'http://bmwofchampaign.com', 'https://pvpd.com', 'http://www.poisonivysalon.com.', 'http://www.rmfenceohio.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://motherstamales.com', 'http://www.pamier-kabob.com/', None, None, None, 'http://www.mabelsbakery.ca/', 'https://www.hilton.com/en/hotels/clepwht-home2-suites-cleveland-independence/?SEO_id=YELP-HT-CLEPWHT', 'http://www.costco.com/warehouse-locations/henderson-nv-673.html', 'http://www.smiledesigncenterlv.com', 'http://www.mononachinastar.com/', None, 'https://www.trendssalonllc.com', 'http://www.heysugarstudio.com', 'https://www.choicehotels.com/arizona/scottsdale/rodeway-inn-hotels/az437/rates', 'http://www.thorespressobar.com', None, 'https://izzysbakeryandcafe.com', 'http://tonydblc.webs.com/', None, 'https://www.teamlogicit.com/PhoenixAZ302/', '1592156578', 'http://clickserve.dartsearch.net/link/click?lid=43700006430431858&ds_s_kwgid=58700000444952719&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', '1592156585', None, 'https://www.palmetto-eye.com', 'http://www.solaireonscottsdale.com/', 'http://www.westernreservehospital.org', 'https://www.sleepcountry.ca', 'http://theupsstore.ca/148', 'http://www.vip-pools.com', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89084/600-in-north-las-vegas/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-600&utm_content=website-link&howheard=IYE', None, 'http://7eleven.ca/store-locator/33259', 'https://www.popeyescanada.com/maps/toronto-liberty-village.html', 'http://www.theproducebox.com', 'http://www.elitepestcontrolnv.com', 'https://www.worldwidegolfshops.com/locations/van-s-golf-shops-mesa-801-s--power-road.html', None, 'http://www.wearejoviec.com', 'http://www.zajecpainting.com', 'http://www.spicy-garden.ca/', 'http://www.pittsburghoralsurgery.com', 'https://www.alterationsandcreationsaz.com', 'http://www.marriott.com/hotels/travel/yyzfs-fairfield-inn-and-suites-toronto-airport', 'http://www.wetseal.com', None, 'http://www.gioninos.com', None, None, 'http://www.gioiabeautybarspa.com', 'http://homedetectiveohio.com/', 'http://www.4seasonstreesllc.com', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.buylaptops.ca/', 'http://www.pittsburgh.va.gov', 'https://hoame.ca/contact-us/', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', None, 'http://eatzencore.ca', None, None, None, None, None, 'http://www.teamfreemanhomeloans.com', None, '1592156716', None, 'http://www.snapfitness.com/fountainhills', None, 'http://www.scooterscoffee.com', None, 'http://www.szechuanexpress.com/', 'http://baycoins.wordpress.com/', 'http://www.computerlasvegas.com', None, None, 'http://familylawguys.com/contact/scottsdale', 'https://www.sephora.com/happening/stores/phoenix-jcpenney-at-ahwatukee-foothills', '1592156756', None, 'http://www.swanpizza.com', 'http://cartridgeworldphx.com', 'http://www.amerizonaproducts.com', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.bridlewoodmall.ca/', None, 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=clein&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', None, 'http://www.faithculture.ca', '1592156791', 'http://www.itsugar.com', 'https://local.fedex.com/az/phoenix/office-5048/', '1592156801', 'http://www.monkeybargym.com', None, None, None, None, 'http://www.quiktrip.com/', 'http://www.signaturewellness.org/', 'http://junipergrill.com', 'http://www.michaudscatering.com', 'http://www.bikeandforth.ca', 'https://www.artlewinbespoke.com', None, 'http://azteamania.com', 'http://www.miegakoreanbbqcleveland.com', None, 'http://goldenasiancuisine.com/', 'http://southparkvet.net/', 'http://www.tamcapturesphotography.com', 'http://www.glotique.com/', 'https://www.t-mobile.com/store-locator/az/chandler/chandler-fashion-center?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://asapcity.com', 'https://www.idealimage.com/medspa-locations/nevada/las-vegas-nv-area/lasvegashendersongreenvalley', 'http://Www.ktsfish-chicken.com', 'http://dreamdinners.com/main.php?page=store&id=53', 'http://www.rockstarhotdogs.com/', None, 'http://www.scottsdaleaz.gov/scottsdale-stadium', '1592156886', 'http://www.discountfirearmslv.com', 'http://www.homelife.ca/office_agents/2164', 'http://www.pillarwestgate.com', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', 'http://www.treasureisland.com/restaurants/little_richies.php', None, 'https://noracleveland.com', 'http://www.cabelas.ca/find-a-store/calgary/14', 'http://www.nevadagastro.com', 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'https://www.extraspace.com/storage/facilities/us/arizona/chandler/1000000272/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', '1592156922', 'http://www.big4motors.com', 'http://telemindclinic.com', 'https://www.wildblue.studio', 'http://theistanbulgrille.com', 'http://www.dunkindonuts.com', 'http://www.fluorescentnails.com', None, 'http://www.leveloneaz.com', 'http://www.summitmedicalweightloss.com/', 'http://hopesbridalnc.com', None, None, 'http://www.meninkilts.com/calgary', 'http://www.harkins.com', None, None, None, None, None, None, 'http://www.marriott.com/hotels/travel/cltfm-fairfield-inn-and-suites-charlotte-matthews/', 'http://luvcuts.com', 'http://www.toronto.ca/parks/parks_gardens/allangdns.htm', 'http://www.abrazadental.com?utm_campaign=local&utm_medium=citations&utm_source=yext', None, None, 'https://www.take5oilchange.com/locations/oh/mayfieldheights-130/', '1592157006', 'https://www.ihop.com/en/restaurants-gilbert-az/920-s-gilbert-rd-1529', 'http://www.murillocarpet.com/', 'https://www.levinfurniture.com/furniture-store/pa/pittsburgh/5438-baum-blvd', None, 'http://www.stanfordcapitalloans.com', 'http://www.jpgexhaust.com', None, None, None, 'http://www.cpr4yourcar.com', 'http://lulyssalonllc.weebly.com/', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/328+Cochran+Road-Mount+Lebanon-PA-15228/storeid=5094?cid=ps_ylp_2020', 'https://www.macu.com/branch-locations/az/gilbert/gilbert-branch/0146', None, 'http://www.JimmyJohns.com', 'http://www.cpr-savers-training.com', 'https://www.paviliondentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.trane.com/residential/en/buying-a-trane/find-a-dealer.html/401830', None, None, 'http://www.carvel.com', 'http://baliandbeyond.ca', 'http://www.karaokerentalphoenix.com', 'http://www.eggsmart.ca', None, None, 'http://www.vogava.com', 'http://www.mrcookschinesecuisine.com', None, 'http://streetsofnewyork.com/', None, 'http://www.truphysicaltherapy.com', 'http://savagewalker.com', 'http://www.tntauctionssnelgrove.com/', 'http://goodworksautorepair.com', 'http://www.hikethislasvegas.com/', 'http://www.pacificforesightsecurity.com/free-security-yelp', None, 'http://www.oneluckypup.com', 'http://www.stovalldentistry.com', 'https://www.dominos.com', None, 'http://www.plushsalonaz.com', 'https://www.kaizenprogressivehealth.com', 'http://www.stoppleworthplumbing.com/', 'http://www.customfitdj.com', None, 'http://www.autodealzaz.com', None, 'http://www.smoothieking.com', 'http://floweramaofglendale.com/', 'http://benedictinewomen.org', None, 'http://www.purevanityspa.com', 'http://www.salonentro.com', 'http://www.shell.us/', 'https://canyonstateclassics.com/contact', 'http://Slicersonmain.com', 'http://www.1brotherspizza.com', None, None, 'https://www.aa.com', None, 'http://www.drlfish.com', 'http://dowdentalcare.com', 'http://www.dignitymemorial.com/funeral-homes/mesa-az/melcher-mortuary-mission-chapel/4527', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.rotorooter.com/scottsdaleaz', 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', None, None, 'https://kottasushi.ca', 'http://www.medvetforpets.com/location/medvet-akron/', 'http://www.internationalhotel.ca', 'http://www.lonemortgage.com', None, 'https://toothworks.com/toothworks-bay-adelaide-dental/', 'http://www.steves-auto-service.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.valleyhomepros.com', 'http://www.smallbarclt.com', None, 'http://www.toscanacondorentals.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281379878&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'https://www.goldbergcentre.com', 'http://www.roosterskountrykitchen.com', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89102/838069/', 'https://www.altierus.org/campus/henderson', 'http://www.coach.com', 'https://medmen.com/stores/scottsdale-north-scottsdale-airport', 'https://hihidonuts.business.site', 'http://www.bulwarkpestcontrol.com/', 'http://ranchoflooringvegas.com', '1592157278', 'http://www.JimmyJohns.com', 'https://www.phoenix.gov/publicworks/garbage/disposable', None, 'http://singsing.com', 'https://aestheticrevolutionlv.com', None, 'https://www.pimtmassage.com', 'http://www.cocosbakery.com/', 'https://www.capriottis.com', 'http://acewasherservice.com/', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'https://www.socialsecuritybranch.com/nv/henderson/henderson-social-security-office/10416-s-eastern-avenue/', 'http://www.collisionrepairphoenix.net', None, None, None, None, 'https://www.olivegarden.com/locations/az/scottsdale/scottsdale-e-cactus-rd/1234?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:scottsdale-az-1234_pl:locurl_rd:1175', 'http://www.jimscoins.com', None, 'http://serenitycleaningaz.com', 'http://www.reddoorliving1.com/delta-lakewood/', 'https://rdavis.amerifirstloan.com', None, None, None, None, 'http://www.tbdnursery.com', None, 'http://www.thescottresort.com/?utm_medium=enhanced-profile&utm_source=yelp', 'https://www.hafezpersianrestaurant.com', 'https://www.zaxbys.com/locations/ga/monroe/195-martin-luther-king-jr-blvd/', 'http://www.yetifirearms.com', None, 'http://www.bombaypalacetoronto.com', None, 'http://lebanesebakery.ca/', 'http://www.midabui.com', 'http://www.whoolisbarandgrill.com', 'https://www.yourcupcakequeen.com', 'http://www.banfield.com/veterinarians/pa/monroeville/moe?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'https://www.vannormanlaw.com', 'http://www.eaglehomeinspections.net', 'https://www.anytimefitness.com/gyms/372/Huntersville-NC-28078/?utm_source=yelp&utm_medium=local', 'http://oralsurgeryaz.com', None, 'http://www.cyclevegas.com', 'http://www.masteryoon.net', 'https://www.brighton.com/viewstore/123', None, None, '1592157435', 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://www.soundplumbinglv.com', 'https://www.envision1361.com', 'http://www.gurusweets.ca', 'http://rebathandkitchens.com', 'https://locations.theupsstore.com/pa/pittsburgh/4885-mc-knight-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.nikolastreeservice.com', 'https://www.doctorallenwellness.com', None, 'https://www.dominos.com', 'https://www.ncfdentistry.com', 'http://www.vervehairdesign.com', None, '1592157478', 'http://www.lossombreros.com', '1592157484', None, None, 'https://local.fedex.com/az/tempe/MSCA/', None, 'http://www.ilovesushihenderson.com', 'http://www.okraaz.com/', 'http://www.starbucks.com/store/9298/', 'http://mascariauto.com', 'http://www.azdanceproject.com/', 'http://www.thetilestore.ca', 'http://www.germancarscottsdale.com', 'http://fracturedprune.com/location/shops-norterra', 'http://tasty-chinese.com', 'http://www.haydeedocasarmd.com', None, 'http://bubblesandsqueak.com', 'http://www.greatclips.com/salons/6225', 'https://www.unclelouie.com', None, 'http://www.firemeupaz.com', '1592157549', 'https://www.hilton.com/en/hotels/lasdmhw-homewood-suites-las-vegas-city-center/?SEO_id=YELP-HW-LASDMHW', None, None, '1592157562', 'https://yonge-and-eglinton.orangetheoryfitness.com?utm_campaign=yelp&utm_term=072017&utm_medium=print&utm_source=redirect&utm_content=yelp_print', 'http://www.beerexpressisbest.com', None, None, 'http://www.omahasteaks.com/stores', None, 'http://www.commonwealthbar.ca/', 'http://www.silverminesubs.com/', 'http://www.presotea.ca', 'http://www.myharu.ca', 'http://www.piedmontgoldexchange.com', '1592157598', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://crclasvegas.com', 'http://www.wildwingrestaurants.com/franchisees/newmarket-north/', 'http://www.apples4you.com/', None, None, 'http://www.marinersmadison.com/', 'http://www.century21.com', 'https://www.mcdonalds.com/us/en-us/full-menu/123dollarmenu.html?cid=PS:GCM_MOP:NB::Yelp:All', 'https://www.choicehotels.com/CN387?mc=blypypaf', 'http://www.vegasinkandtoner.com/', 'http://www.johnvarvatos.com/storedetails?StoreID=5656', 'http://www.westsidecommunitymarket.org', 'http://richnerair.com', None, 'https://www.kwiktrip.com', '1592157649', 'http://www.starbucks.com', 'http://www.timhortons.com', None, 'https://www.thejoint.com/north-carolina/huntersville/birkdale-12006', 'http://www.lukehousemadison.org', 'http://www.greatclips.com/', 'http://local.firestonecompleteautocare.com/arizona/phoenix/3638-e-thomas-rd/?lw_cmp=IYP_YPC_MLP_13315', 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', None, 'http://www.smokeandjoelounge.com', None, 'http://botecolv.com', 'http://www.keelinglawoffices.com', 'https://puredentalaz.com/home.htm', 'https://www.thewestlake.ca', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.greyhound.com/social?utm_source=Book%20now&utm_medium=Yelp&utm_campaign=permanent%20link%20', 'http://aaronmachineshop.com', 'http://www.vegasprohvac.com', None, None, None, 'http://www.torontoimageworks.com', None, None, 'https://desertrad.com/locations/southwest-wynn-road', None, 'http://rocksolid-surfaces.com', None, None, 'https://www.lappeneyecare.com', 'https://www.bentosushi.com', 'http://www.drrusselo.com', None, 'http://www.dunkindonuts.com', 'http://nouveauxclt.com', None, None, 'http://Pizza-wings.com', 'http://tracysautobody.com', None, None, 'https://www.marquiscompanies.com/facility/marquis-plaza-regency/', 'http://www.nascarspeedpark.com/nc.aspx', None, None, 'https://www.gowireless.com/store/stores/Arizona/Mesa/Mesa---MonteVistaVillageCenter----602609', 'http://www.kwikfill.com', 'http://www.usps.com', 'http://www.dolcegelato.net', 'https://www.hilton.com/en/hotels/pitokhx-hampton-pittsburgh-university-medical-center/?SEO_id=YELP-HP-PITOKHX', 'http://www.exclusivetailoring.com', 'https://www.martinandmacarthur.com/', None, 'http://www.marleypark.com/', 'http://www.corepestsolutions.com', 'https://www.marcustheatres.com/', 'https://www.dippindots.com/loc/ll/US/NC/Charlotte/6801-Northlake-Mall-Dr_', 'http://www.healthydentalalternatives.com', 'http://www.northmountainvisitorcenter.org', '1592157819', None, 'https://www.fjtesq.com/?npcmp=dir:local:4407007:89145', None, '1592157829', 'http://www.mwuclinics.com', 'http://www.windowprollc.com', 'http://www.azairductcleaning.com', None, 'http://www.aamcolasvegas.com', 'http://www.casinonight2you.com', None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.dairycream.org/', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_426', 'http://www.ntb.com/store/8522/bedford-oh-44146-2252?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, 'http://www.lovebailbonds.vegas', 'http://downtownfood.ca/', '1592157877', '1592157879', None, 'http://www.apollos.com', None, None, 'http://www.dairyqueen.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://bennysva.com', 'http://urbantealoft.com/', None, None, 'http://www.25celciusbeautybar.com', 'http://www.simplicitylaser.com/locations/nevada/henderson/', 'http://www.hopkinsautospa.com', 'http://www.junk-rite.com', 'https://locations.dennys.com/NV/LAS-VEGAS/247828', None, 'http://www.arborealty.com', None, 'http://www.9dragonskungfu.com/', None, 'https://www.storquest.com/self-storage/az/tempe/9052', None, 'http://www.nailswithlovelv.com', 'http://www.daveyplumbingpittsburgh.com', 'https://birdysoulfood.com', 'http://motorsandmoreinc.com', None, 'http://www.steaknshake.com/locations/24097-steak-n-shake-us-hwy-17-s-brunswick', 'http://surprisefamilymedicine.com', None, 'http://www.czcustom.com', 'http://Dogfather.me', 'http://clickserve.dartsearch.net/link/click?lid=43700006430792752&ds_s_kwgid=58700000444978432&ds_url_v=2', 'http://www.kelseys.ca/location_region.php?province=on&s=1&city_drop=North+York', None, 'http://jianphoto.com/', 'http://www.worldofdecorauctions.com', 'http://www.goodwillsp.org/shop/retail-stores/pineville/', None, None, None, 'http://www.childrensorchard.com/stores/las-vegas-nv/', None, 'https://www.walmart.com/store/3473/las-vegas-nv/whats-new', 'https://www.pescadoborracho.com', 'http://www.spiceshack.ca', None, None, None, '1592158252', None, None, None, 'http://www.extendasuites.com', None, None, 'http://www.docautorepairs.com', 'https://www.signaturestyle.com/locations/oh/medina/famous-hair-medwick-marketplace-haircuts-67153.html', None, '1592158276', None, 'https://www.luxor.com/en/nightlife.html', '1592158284', 'http://www.southstburger.com/location/35-first-commerce-dr/', None, 'http://shopmelrosevintage.com/', 'http://www.mrsub.ca', 'https://imwireless.net/locations/concord-ma/', 'https://lasvegaspainreliefcenter.com', None, 'https://www.extraspace.com/storage/facilities/us/arizona/mesa/501578/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.fastfreshfoods.ca/', None, 'http://www.zazaespressobar.com', 'http://www.snapfitness.com/gyms/lasvegas-nv-89147/7089', 'http://www.forever21.com', 'http://www.ssmokincafe.com', None, None, None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Carnegie-PA-15106/067741/', 'http://www.saloncafe.net', 'https://www.blumenailsspasolon.com', 'http://www.gehendricks.com/', 'https://www.norfolkhall.com', 'http://missionptaz.com', 'http://www.visithenderson.com/todo/special-events/stpatricksdayparade', 'http://www.skinapeelbeautybar.com', 'http://www.ccdcranch.com', 'http://www.craftdogs.com/', None, 'http://www.tomatoesiipizzeria.com/', 'http://yesidobridals.com/', 'https://www.lumberliquidators.com/ll/stores/az/mesa/1845-south-power-rd?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1388', None, None, 'http://www.walmart.ca', 'http://www.papajohns.com', 'http://www.partycity.com/storedetail.do?id=842', 'http://locations.tccrocks.com/az/scottsdale/8980-e-indian-bend-rd.html', None, None, None, '1592158380', 'http://www.raxlenpharmacy.com', 'http://www.anjapparcanada.ca', None, 'http://www.dennys.com', 'https://www.ispynserve4u.com', 'http://mainstreetautoservices.com', 'http://www.dennyscarwash.com', None, 'http://www.bk.com', 'http://www.eatgenos.com', None, 'https://www.seeeyewear.com/locations/pittsburgh', None, 'https://www.piesbyinge.com', 'https://locations.nekterjuicebar.com/ll/US/AZ/Tempe/2000-E_-Rio-Salado-Pkwy_*-Ste_-1213?utm_source=yelp&utm_medium=link&utm_campaign=Tempe&utm_content=URL', 'http://kohinoortempe.com', 'http://idolizespa.com', 'http://www.naturaltress-salon.com', 'https://www.sunrisepreschools.com/locations/baseline-gilbert/?utm_source=yelp&utm_campaign=online_listing_gilbert_280&utm_medium=referral&utm_term=business_url', None, None, 'http://www.peridotsweets.com/', None, 'http://www.thefitmenswear.com', 'http://thegrillat11union.com', 'http://www.papajohns.com/', None, 'https://www.victoriassecret.com', 'http://www.lostdutchmanroasters.com', 'http://www.petplanethealth.com/stores/village-plaza/', None, None, 'http://www.upinvapor702.com', 'https://www.ronmarhoferchevy.com', None, None, 'http://www.sanealcamera.com', 'https://www.bankofamerica.com', 'http://www.thesinginglady.com', 'http://clickserve.dartsearch.net/link/click?lid=43700006435127049&ds_s_kwgid=58700000444950373&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.arizonaeyecenter.com', None, None, 'http://www.thespicetrader.ca/', None, None, 'http://www.harkinstheatres.com/', 'https://chefmayra.com', None, 'http://www.westmore.ca', None, 'http://www.LaRoccaKitchen.com', 'http://www.craquedecreme.com', 'https://heartandlungnv.com/physicians/profile/Arnold-Chung-MD', None, 'http://www.loveandkissespetsitting.net', None, None, 'http://www.tsgservicesaz.com', 'https://www.staples.com', None, None, None, 'http://carlosthecomputerguy.com/', 'http://info.tradesecrets.ca/locations-reviews/upper-canada-mall/', None, 'https://www.shapirolawaz.com', 'http://www.azpatiocover.us', 'http://bevvyuptown.com', 'http://Www.solasalonstudios.com/salon-professional/liz-mervar1', None, 'http://www.yangschicken.ca', None, 'http://www.dsw.com', None, None, 'http://birdhauscoffee.com', None, 'http://www.jysk.ca', None, 'http://www.puffnstuffstores.com', 'https://www.brakesplus.com', 'https://locations.noodles.com/pa/pittsburgh/476-mcmaster-way.html', 'http://www.michaeltoddsfurniture.com', None, 'http://www.dentistryintoronto.com/', 'https://jmichaelrealestate.com', None, 'https://splittingtimber.com/axe-throwing-phoenix/', 'http://www.crabhouselv.com', None, 'http://wisconsincutlery.com/', None, 'http://www.jerseygiant.ca', 'http://www.mazdaofrichmondhill.com', 'http://www.quiktrip.com', 'http://www.dimsumchineserestaurant.com', 'http://www.marcustheatres.com', None, 'http://kaiburcoffee.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.shishaliciouscafe.ca', None, 'http://charandamexicaneatery.com', 'http://www.rideprlimo.com/scottsdale-limousine/', 'http://www.distillata.com', 'http://www.sobeys.com/en/stores/sobeys-aurora-bayview/', 'http://www.acanac.com', 'https://www.ubreakifix.com/locations/goodyear', 'https://www.robainalaw.com', 'http://www.newdimensionsauto.com/', 'http://www.martinmarineaz.com/', None, None, 'http://www.rexall.ca/', 'http://www.baierlhonda.com', 'http://www.pizzalafelice.com', None, 'https://www.olivegarden.com/locations/wi/madison/madison-east-towne-mall/1300?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:madison-wi-1300_pl:locurl_rd:1227', 'https://www.chilis.com', 'http://www.npfy.org', 'http://www.bedbathandbeyond.com', 'http://www.andersons.pub', 'https://www.lowes.com/store/AZ-Scottsdale/1850', 'http://www.playfactoryparty.com', None, 'http://cityh2o.com', 'http://www.zooecomuseum.ca/', 'http://www.shamsflorist.ca/?srccode=yelp_track', 'https://massagetherapistscottsdale.com', 'http://www.wilshirepines.com', 'http://www.modernfurniturestudio.com', 'http://allontarioapplianceclinic.ca', 'http://www.bridalalterationspittsburgh.com/', 'https://perfumecollection.ca', None, 'https://www.homedepot.com/l/Ray-Road/AZ/Chandler/85226/476?cm_mmc=seo-yelp&', 'http://www.bornandraisedlv.com', None, 'https://www.statefarm.com/agent/us/nv/las-vegas/ladonna-koeller-p89cl1ys000?cmpid=jxep_blm_0006', 'https://www.jewelrymedinaohio.com', 'https://eastendpittsburgh.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'https://www.choicehotels.com/wisconsin/madison/cambria-hotels/wi143/rates', 'http://www.cafe-mirage.com', None, 'http://adagestudios.com', 'https://www.masteroftintllctempe.com', None, 'http://lsmchiro.com/clinics-office-hours/sunprairie.html', 'http://plumbing-repair-now.com', 'http://spookysswirls.com', 'http://www.sunserimove.com', None, 'http://www.nandos.ca/restaurants/bay-street', 'http://www.massageheights.com/south-pointe-plaza', 'http://www.a-zsources.ca', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', 'http://www.smilereef.com', 'http://simplycardio.com', None, 'http://kismetandclover.com/', 'http://www.assouline.com', 'http://www.pkcreek.ca/', 'http://www.internationalgalleriesurbana.com', 'http://www.regularsbar.ca', 'http://www.6DegreesAZ.com', 'http://www.oldnavy.com', None, 'http://www.dmcsystemsllc.com', 'http://www.jumpstartchildcare.com', None, 'http://www.villapizza.com', 'https://www.yourlistingexpert.com', 'http://stores.dsw.com/usa/nv/henderson/dsw-designer-shoe-warehouse-stephanie-street.html', 'https://www.usps.com/', None, 'https://eastvalleyrv.com', None, '1592158816', None, None, None, 'https://www.aircanada.com/ca/en/aco/home/fly/premium-services/maple-leaf-lounges/maple-leaf-lounge-details.html#/!lounge@toronto', 'http://chickswithspiritualgifts.com', None, 'http://www.costco.com/', '1592158831', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.tyddvegas.com', 'http://www.samfawazphotography.com', None, None, 'https://www.schendelpest.com', 'http://www.honeybeeac.com', None, 'https://www.gavishpropertymanagement.com', 'http://www.topnailsaz.com', 'http://www.katesissons.com', 'http://www.JimmyJohns.com', 'https://plexustechnology.com', 'http://www.thedirtydrummer.com', 'http://pac.unlv.edu/index.php', 'http://www.enterprisecarsales.com/location/5482/Enterprise_Car_Sales_Las_Vegas?mcid=iyp:277&CUR=yelp', 'http://www.happitimedaycare.com', None, '1592158875', 'http://www.wyldewoodillinois.com', None, None, 'http://www.tribridpersonaltraining.com', 'http://www.kw.com', '1592158885', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.azheart.com/', None, 'http://www.bellabridesmaids.com/', 'http://www.dollargeneral.com/', None, 'http://www.plazahotelcasino.com/entertainment/the_best_little_wh', 'http://www.yofreshyogurtcafe.com', 'http://mdskinlounge.com', None, '1592158911', 'https://www.itdrsolutions.com', 'https://www.papajohns.com', 'http://hiltongardeninn3.hilton.com/en/hotels/ontario/hilton-garden-inn-toronto-oakville-YTOTVGI/index.html?SEO_id=YELP-GI-YTOTVGI', None, 'https://www.emser.com', 'https://locations.jackinthebox.com/us/ca/glendale/1200-w-glenoaks-blvd', None, 'http://www.pitapitusa.com/', None, None, None, 'http://www.tlcdentalcarelv.com', None, 'http://www.chiefsautowash.com', 'https://www.gamesourceinc.net', None, None, None, 'http://www.bigotires.com/Locations/89032', 'http://www.mbenergetics.com', None, '1592158958', '1592158961', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.goldenchinarancho.com', 'http://www.starbucks.com/store/14175/', 'https://www.cellphonerepair.com/monroeville-pa/', 'http://vbarbershop.com/locations/kierland-scottsdale/', 'https://agents.allstate.com/padma-schaudt-las-vegas-nv.html', 'https://www.petsmart.ca/stores/ca/on/oakville-store2002.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', '1592158979', 'http://www.designedbydyani.com', 'http://spadinaoptometry.ca/', 'https://www.wellschiro.com', 'https://www.justonemoretavern.com', 'https://www.sprouts.com/stores/details/-/store-details/view/store/7/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.framestorepittsburgh.com', None, 'http://totemappliance.com/', 'http://www.silvertoncasino.com', 'http://playnwisconsin.com', 'http://www.tokasticksgolf.com/index.php', 'https://local.biglots.com/nv/las-vegas/4500?zcp=pd_local_yelp', 'https://www.dwellarizona.com', 'http://achermanlaw.com/', 'http://www.odellconstructioninc.com', None, 'http://www.thebownesiangrocer.ca', 'http://outlandcigars.com', 'http://stlouiswings.com', 'http://www.brokeassphone.com/broke-ass-phone-locations/broke-ass-phone-rocky-river-ohio', 'https://www.valleywidecooling.com', None, 'http://www.amrracing.com', 'http://www.cmlibrary.org/locations/branches.asp?id=13', None, 'http://nakedpizza.biz', 'http://www.meltinyourmouthcupcakes.com', 'https://local.fedex.com/az/phoenix/office-5048/', 'https://locations.usbank.com/index/arizona/gilbert/east-baseline-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.dominos.com', 'http://www.treeworkersofphoenix.com', 'http://d-moes.com/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://dansdogsdiner.com', 'http://www.saucepizzaandwine.com/locations/scottsdale-scottsdale-waterfront/', None, 'http://Www.tomjames.com', 'http://www.healinginspirations-wi.com/', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', '1592159067', 'https://stores.advanceautoparts.com/pa/etna/500-butler-street?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', None, 'https://local.fedex.com/nc/charlotte/office-0746/', 'https://northvalleysurgerycenter.com', 'http://www.burritozone.ca', 'http://www.enterprise.com/car_rental/deeplinkmap.do?cnty=US&gpbr=53W9&bid=004&arc=YAPL100&cm_mmc=Yelp-_-Local-_-National-_-null', 'http://pddlv.com', 'https://hairbykee.wixsite.com/hair-by-kee', None, None, '1592159093', 'http://www.trianglebarswissvale.com', None, None, None, 'http://freshco.com/stores/bloor-dundas', 'http://www.bojangles.com', 'http://www.mark-taylor.com/arizona/san-sonoma/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.midhafurniture.com', None, None, 'https://www.lashandskinlab.com', None, None, None, None, 'http://www.serviceking.com/locations/service-king-bell-rd?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', None, None, 'http://alatisinspectionservice.com/lp/home-inspection', 'https://www.moes.com/find-a-moes/pennsylvania/bridgeville/938?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', None, 'http://www.wagg-n-walk.com', 'http://www.clevelandcabby.com', 'https://www.chaoshomeloans.com', 'http://www.marondahomes.com', 'http://www.morocochocolat.com/', 'http://anytimefitness.com/North-Royalton', 'http://qualitysystemsac.com', 'https://local.safeway.com/safeway/az/sun-city-west/13503-camino-del-sol.html', 'http://www.buckinghamsports.ca/view/buckinghamsports/the-penalty-box', 'http://geckohomeservices.com', 'http://www.republicwesthome.com', 'http://www.pawlorpets.com/', 'https://www.sevabeauty.com/location/az/avondale-w-rancho-santa-fe-blvd/', 'http://www.tjmaxx.com', None, None, 'http://www.barleyhousecleveland.com/', 'http://www.landmarkcinemas.com/bolton/contact-us', '1592159181', 'http://www.irenevoo.com', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', None, None, None, 'http://www.cumbraes.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://www.curtisnewsomedds.com', 'http://walmart.com/', 'https://www.scottsdalemoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://www.casinomontelago.com', None, None, None, 'http://www.jaguarnorthscottsdale.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Mesa-AZ-85210/723081/', None, 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1368', None, 'https://www.viomedspa.com', 'http://www.paradisetileandnaturalstone.net', None, 'http://www.kinglawofficespc.com', 'http://www.innovateframe.com', None, 'http://www.happyhourarizona.com/champions-sports-saloon', 'http://www.millcrestpark.com', 'http://www.atlanticbay.com', 'http://www.fiddlersdream.org', 'http://www.nationaleventstaffing.com', 'http://holisticfit.life', 'http://www.atwistedtulip.net', 'https://www.carmax.com/stores/7284?adcode=YLP7284&utm_campaign=LG_AFF&utm_source=LG_AFF_YLP&utm_medium=local&utm_content=shop', None, None, None, 'https://stewardship.pro', 'http://www.golfsmith.com', 'http://www.duskscottsdale.com', None, 'http://www.metrosouthbridge.com', 'http://www.pizzahut.com/', 'http://www.80OnGibsonapts.com?campaign_code=yelp_80_On_Gibson_NV_89012', 'http://reliableappliance.ca', 'https://www.legendsofchampaign.com', 'http://www.timhortons.com/ca/en/locations/get-directions.php?id=101357', None, None, 'http://www.spotlesssquadlv.com', None, 'https://asquaredmathtutoring.com', 'http://www.autoxpertslv.net', None, 'http://www.shanklelaw.com', None, 'http://www.cajuncrawfishLV.com', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1165', 'https://ohiosbestmassage.com', 'https://handandstone.com/locations/az-glendale', '1592159307', '1592159309', 'http://inesdisanto.com/', 'https://www.mandalaybay.com/en/nightlife/eyecandy-sound-lounge.html', None, 'http://affordablemoverslv.wixsite.com/website', None, 'https://pizzapit.biz', 'http://www.piedmontexpresscaresuttonroad.com/', 'http://www.distinctiveweddingvideos.com', None, 'https://affderm.com/locations/tempe-office/', 'http://vegasproperty.management', 'http://www.gandmstaffingsolutions.org/', 'http://www.bellagio.com/attractions/gallery-of-fine-art.aspx', 'http://www.structube.com', None, 'http://www.autocash.com/auto-cash-in-las-vegas?utm_campaign=places&sf_traffic=paid_listing_yelp&utm_medium=listing&tmx_id=d2c199521a9a9f&utm_source=yelp', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.theavenuebanquethall.com', None, None, None, 'http://trutea.ca', 'http://www.rbomotorsports.com', None, '1592159362', 'http://thebagelshoppe.weebly.com/', 'http://www.freewayinsurance.com', 'http://www.persianbijar.com', 'https://www.phoenixmusiclessons.com', 'http://www.discoverydetectivegroup.com', 'http://www.fortinos.ca/en_CA/storedetail.484.html', 'http://www.motel6.com/reservations/motel_detail.aspx?num=4742', 'http://www.its2di4.com', None, 'http://pawminderspluspetsitters.com', 'http://www.fiatusaofstrongsville.com', 'http://www.skinsopretty.com', 'https://www.ontario.ca/page/serviceontario', 'http://www.northphoenixcampground.com', 'http://www.packbrotherscollisioncenter.com/', 'http://www.gusnewyorkpizza.com/', None, 'http://www.canadianpardons.ca', 'http://www.computerezearizona.com', None, 'http://www.vashticosmetic.com', None, 'http://fitforlifefood.com/', 'https://www.meijer.com/shop/en/store/307/?cmpid=OLA:040319:YelpGrocery', None, 'http://www.suepembertoneducation.com', 'http://www.disktopia.com', 'http://www.wjbonline.com', 'http://www.atriasrestaurantpncpittsburgh.com', 'http://www.discotech.me', 'http://www.myturnlv.com', None, 'http://www.catchacritter.us', None, None, 'http://www.ourfamilyeyecare.com', 'http://www.goodwillaz.org/', 'http://www.BroadstoneParadiseValley.com/?utm_medium=listing&utm_source=yelp', 'http://uptownnailsalon.wix.com/uptown-nail-salon', 'https://www.sticyyc.com/locations-1/', 'http://www.harveyswineburger.com', 'http://esoslifestyle.com', 'http://www.smithenvironmentalsolutions.com', 'https://beyondextensions.mayvenn.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.cardinalewaymazdapeoria.com/?ibp-adgroup=yx_target', None, '1592159462', 'https://local.albertsons.com/az/peoria/8240-w-deer-valley-rd.html', None, 'http://www.plastikwrap.com', 'https://www.petsuppliesplus.com/Store/OH/Lakewood/Lakewood/128', 'http://www.thunderbirddental.com', 'http://poolservlv.com', 'https://www.heinens.com/Heinens-of-Hudson', 'http://www.jackscornertaplkn.com/', None, None, 'https://www.wyndhamhotels.com/hotel/03725?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:03725', 'https://innovativecleaningsvs.com', 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', 'http://www.statusinkllc.com', 'http://bellagiopizza.ca', 'http://www.puptowncharlotte.com', None, 'http://www.starbucks.com/store/10311/', 'http://avis.com', None, 'https://locations.postnet.com/nv/las-vegas/10120-w-flamingo-rd', 'http://aftbar.com/', 'https://local.skechers.com/az/phoenix/', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.autozone.com/locations/az/peoria/8669-nw-grand-ave.html', 'https://smartmoveinsurance.com', None, None, 'http://www.the-idea-store.org', 'http://www.dunkindonuts.com', 'https://www.i9sports.com/ProgramDirector/309/', 'http://www.rainrestaurant.ca', 'http://www.davidandgoliathtees.com/', 'http://www.starrdickensortho.com/', 'http://mickeles.ca/', None, 'http://www.westsidelaser.ca', 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?STORE=629&language=EN', 'https://gilbert.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, 'http://www.pitapit.com', 'http://www.cottonwoodstationeatery.com', 'http://superdiscounttrans.com/', '1592159557', 'http://www.bowlingwithleverage.com', 'http://www.saloncentric.com/', 'https://www.carolinashealthcare.org/locations/detail/carolinas-healthcare-urgent-care-union-west', 'http://www.autosonic.ca', None, 'https://www.heirloomtoronto.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.66065.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:66065', 'http://philipsplastics.com/', 'http://www.bookmans.com', 'http://www.wordofmouthdentistry.ca', 'http://www.starbucks.com', None, 'http://www.yofreshyogurtcafe.com', 'http://www.breadheadslv.com', 'http://www.luxor.com/attractions/attractions_king_tut_museum.aspx', 'http://www.crazymocha.com', 'http://www.vuaurology.com', 'http://www.costco.com/', 'http://www.mydcdental.com', 'http://www.ritzcarlton.com/en/hotels/charlotte/dining/punch-room', 'http://phoenicianestates.com/', 'http://www.bountifulfruitarrangements.com', '1592159602', None, None, None, None, None, 'http://www.azpowerwashpros.com', 'http://www.fishcreekvets.com/', 'https://haircutmensoutheuclidoh.com', 'http://Www.mixnmatchausa.com', None, 'http://consolidatedauto.com', None, 'http://www.cookinsgroup.com', 'https://stores.bestbuy.com/il/champaign/2117-n-prospect-ave-46.html/?loc=ns100&ref=NS', 'http://www.nextcare.com/locations/az/peoria-glendale/?utm_source=Yelp&utm_medium=Local&utm_campaign=peoria_glendale', 'http://darkhorsesportsbar.com', None, None, 'http://www.catseyevintage.ca', 'http://www.searsgaragedoors.com', '1592159643', 'http://www.westcoastkids.ca', 'http://heavenlyhairbodysalon.com', None, None, None, '1592159653', 'http://www.cyclonespitas.com', None, None, None, 'http://www.valledelsol.com', None, 'http://www.villageinn.com/', None, None, None, 'http://www.tascsolutions.org/locations/phoenix-central', 'http://hooverdamstore.com', None, 'http://www.elitepodiatry.net', None, '1592159685', 'http://www.cleverchefscatering.com/', 'http://www.successjustclicks.com', None, 'http://www.theterracegardens.com', 'http://www.nortownfoods.com', '1592159695', None, 'http://www.chinadragonbedford.com', 'http://www.choiceautorepairaz.net', 'http://gpsandtrack.com', 'http://www.pancheros.com/locations/tempe', 'http://www.oldvegastavern.com', 'https://store.vioc.com/wi/madison/3594-e-washington-ave-53704-GR0030', '1592159710', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.youfit.com/gym/scottsdale-scottsdale-rd-7346?utm_source=local&utm_medium=yelp&utm_campaign=club7346&utm_term=website', 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.budget.com/', 'https://www.glamparlor.com/?utm_source=Yelp&utm_campaign=Main_Web', None, 'http://www.balanicustom.com/custom-suits-cleveland/', None, 'http://www.cox.com', 'http://www.westendcomics.ca', 'http://www.greenhousemontessorischool.com', 'http://carpetwarehousecleveland.com', None, None, 'http://www.ontrac.com', None, 'http://www.jacobsonbrosdeli.com', 'http://www.altrahomedecor.com', None, None, None, None, 'https://p3hp.org/nevada/p3-medical-group/our-locations/business-park/', 'http://lvmpd.com/', None, None, 'http://www.fastforwardskate.com', 'http://www.midoco.ca', None, None, 'https://www.starbucks.ca', None, None, 'http://www.dunkindonuts.com', 'http://www.findyourcenter.com/', 'http://www.neocoffeebar.com', 'http://www.locksmithbetty.com', None, None, '1592159796', 'https://www.walgreens.com/locator/walgreens-4667+william+penn+hwy-murrysville-pa-15668/id=11768', 'http://www.thespa-sunprairie.com', 'http://www.rushhourlegal.com', 'https://locations.jackinthebox.com/us/az/gilbert/4361-e-baseline-rd', None, 'http://www.celsiussushibar.com', '1592159814', None, None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.gamestop.com/store/us/az/glendale/1867/arrowhead-town-center-gamestop', None, None, 'http://www.SonicAutoHouse.com', None, 'http://www.bayviewmooreauto.com/', 'http://www.jessicabashaw.com', 'http://www.thewoodenvine.com', None, 'https://merkatoethiopianrestaurantlasvegas.com', 'http://www.whitevacuum.com', None, None, None, None, 'http://www.beattheheatpoolservice.com', 'http://www.carmellaspizzagrill.net', 'http://www.tphc.ca', 'http://www.tomscountryplace.com', 'http://www.balaton-restaurant.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.autoexinc.com/', 'https://creativenailsandspascottsdale.com', None, 'http://www.canadiantire.ca/en/store-locator/ab/calgary-south-ab.store.html', 'http://rusticsocial.ca', 'http://wolfwatersports.com', 'https://www.extremearizona.com', 'http://www.theBooKnack.com', None, 'https://elementsmassage.com/fitchburg', None, 'https://www.copart.com/locationDetail/47', 'http://tigotrattoria.ca', None, 'http://www.nevadadesertmermaids.com/', 'http://www.caesarsuniforms.com', 'http://www.wingsntings.ca/', 'http://www.boulderzclimbing.com', 'http://www.SonoranVein.com', 'http://www.goodlifefitness.com', 'http://nievemalandra.com', None, 'http://www.scottsdalespice.org', None, 'http://l.macys.com/madison-wi?cm_mmc=Yelp_Stores-_-Madison-_-n-_-228&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Madison_228&m_ac=yelp_stores&m_ag=n', 'http://www.superiortire.ca/locations/mode/7/208-king-rd-oak-ridges-on-l4e2w1.aspx', 'http://thearizonafishingguides.com/index.php', 'http://www.chapmancollision.com/', 'http://www.quiktrip.com/', None, None, None, 'http://www.littlecaesars.com', 'http://www.onereddoorphotography.com', 'http://www.circuscircus.com/casino/slots_a_fun.aspx', None, 'http://www.milgard.com', 'http://benetflorentine.com', 'http://www.sbistroaz.com', None, 'http://locations.avis.com/us/az/chandler/c5a.html', 'http://www.rockcitydance.com', None, 'http://www.washwerksexpress.com', 'http://AutoFinanceNC.com', 'http://www.mrhandyman.ca/calgary-south', None, 'https://arizona.weidner.com/apartments/az/mesa/pala-mesa-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', None, 'http://www.lesterklebedpm.com', 'http://www.bk.com', 'https://www.bathandbodyworks.com', None, 'http://www.brakemasters.com', 'http://clearfloat.ca', None, 'http://www.watchdogpestcontrol.com', None, 'http://www.budgetbridal.vpweb.com', 'http://advancedheartcare.com/', 'https://moxies.com/?utm_source=yelp&utm_campaign=yelp_enhanced_profile&utm_content=landing-page', 'http://www.ihlcanada.com', 'http://www.parmalaserwash.com', None, 'http://www.anatoliaturkishfood.ca', None, None, 'http://calgarylibrary.ca/locations/shaw', 'https://www.payless.com/stores-location/NV-LAS-VEGAS-5798.html', 'https://peoria.uptownjungle.com', None, 'http://www.rimrepairrx.com', None, 'http://www.apria.com', None, 'http://www.santinocatering.com', 'http://www.fusionsincsalonanddayspa.com', 'http://www.qualityonepool.com', None, 'http://zenarizona.com/', None, 'http://empireplumbingac.com/', 'http://www.contourmedical.com', 'https://website-18496976604484669992-seafoodrestaurant.business.site', 'http://www.swimmingpoolrepairphoenix.com', 'https://locations.visionworks.com/ll/US/OH/Beachwood/26300-Cedar-Rd', 'http://www.barrebodystudio.com', 'http://www.wwsdental.com', 'http://robertostacoshop.com', None, None, 'http://pacificeastcoventry.com/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4391+East+Washington+Avenue-Las+Vegas-NV-89110/storeid=3172?cid=ps_ylp_2020', 'http://www.labonitadulceria.com', 'http://www.retinalconsultantsaz.com', 'http://www.irideworldwide.com', 'https://titleboxingclub.com', 'http://www.serviceking.com/locations/service-king-north-las-vegas?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'https://www.elegance-living.com/senior-living/nv/las-vegas/wentworth-las-vegas', 'http://www.cafekrishnaaz.com', 'http://mountaincreektrees.com', None, 'http://www.batw.ca/', None, '1592160137', None, 'https://locations.vitaminshoppe.com/nv/lasvegas/vitamins-supplements-las-vegas-nv-394.html', None, None, 'http://www.secondsoleohio.com/#!akron/c1fn6', None, None, None, None, 'http://www.purpleorchidflowers.ca/', None, 'http://www.bluepandalv.com', 'http://calgary.treehouseplay.com/', 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'http://www.ncdot.org/dmv/', 'http://www.2meatballz.com/', 'https://www.fit4less.ca/locations/ontario/north-york/409?utm_source=yelp&utm_medium=cta&utm_term=torontolawrence-f4l', 'http://www.mrhero.com/', 'http://www.truevalue.com/', 'http://www.pombalensebakery.com/', None, 'http://www.peoriacpr.com/', 'http://www.terribleherbst.com/', None, 'https://www.smartstyle.com/en-us/locations/on/brampton/located-inside-walmart-3135-haircuts-5184.html', 'http://www.massagebymichael.vegas', 'https://www.myeyedr.com/locations/ballantyne?utm_source=Yelp&utm_medium=Referral&utm_campaign=ballantyne', None, 'http://www.reebokcrossfitramsay.com', 'http://blackowlrealtylv.com', 'http://www.speducci.com/', None, 'https://deadcityvegas.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://bostonpizza.com/centropolis-laval', 'https://satruck.org', 'http://www.richbeckguitars.com/', None, 'http://www.inspiringsmilesdentistry.com', None, 'http://www.morcillapittsburgh.com', 'http://www.kids-supergym.com', None, 'http://www.deserthottubs.com', 'http://www.dimaggiostire.com/', 'https://local.fedex.com/nv/las-vegas/office-1441/', None, None, None, 'http://budstreecare.com', None, 'http://www.saintsandsinnershairdesign.com', 'http://www.woodiesautoservice.com', None, 'http://www.gap.com?tid=gpme000290', None, 'http://rawfitnesslv.com', 'http://www.starbucks.com', 'https://cocosgelatooh.com', 'http://www.sissybeautysalon.com', 'http://m.primarycarewalkinmedicalclinic.com', None, None, 'https://www.sprint.com/storefronts/bd/sprint-matthews-nc-28105-fcs-2516/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.xiangcunfaxian.com/', 'http://Www.LVLegalHelp.com', 'https://scottsdale.andaz.hyatt.com/en/hotel/dining/weft-warp-art-bar-kitchen.html', 'http://www.salzmann.com', None, 'http://glossitdetailstudio.com/', 'http://www.trcaparks.ca', 'http://www.eastofchicago.com', None, 'https://chocolateshops.sees.com/pa/pittsburgh/chocolate_shops_pittsburgh_pa_pa-17.html', 'http://houseoffitness.net/', None, 'http://www.circletree.net', 'https://www.atmosphere.ca/stores/calgary.html', 'http://www.burgers2beer.com/', 'http://www.shipleyortho.com/', None, None, 'http://www.mamathaikitchenaz.com', 'http://www.junctionatantiquity.com', 'http://www.vendettatowing.com', None, None, 'http://www.centennialwellnesscenter.com', 'http://thebiomedcenter.com/', 'http://www.LandisReedHomes.com', 'https://www.thegibsoncharlotte.com', 'http://www.vientianepalacerestaurant.com', 'https://www.allauramedical.com', None, 'http://www.benefitcosmetics.com/?ext_id=yelp_ulta_010713_Yelp', 'http://www.cnroofing.com', None, 'http://www.sabas.com', 'http://www.greatclips.com/', 'http://www.mammothairlv.com', 'http://www.daleshirleys.com', None, 'http://www.baldwinbrothersautomotive.com', 'http://www.gyroworldohio.com/', None, None, None, 'http://www.bistro-jules.com', None, 'http://onsitebuilds.com/', 'http://www.livewellarborsteelecreek.com', 'http://www.augiessportsgrill.com/', None, None, 'https://www.gowireless.com/stores/az/gilbert/gilbert-gilbert-road/', None, None, 'http://www.arrabiatas.com', None, 'http://www.heroburgers.com', 'http://www.amesachiropractor.com', 'https://onginstitute.com', 'https://www.woodlandestatesapartment.com', 'http://www.bamboobakery.com', 'http://www.olsonglassandmirror.com', 'http://www.carolinafoxs.com', 'http://www.kingwongchinese.com', 'http://www.midaslocator.com/AutoRepairFinder/tabid/151/Default.aspx', 'http://www.theminderbinder.com', 'http://www.wpinsure.com', 'http://www.sagastasalon.com', 'http://velveteenrabbitlv.com', None, None, 'http://pesterminate.ca', 'http://downtown.muramoto.biz', None, 'http://nevadacheapcars.com/', 'https://www.laserquest.com/nv-lasvegas', None, None, None, None, 'http://smogbusters.com', None, 'http://www.theriverrockgrille.com', 'http://www.myresortspa.com', None, 'http://nalysfloralshop.com', 'http://www.plantitsucculent.com', None, 'http://www.greatclips.com/salons/1552', 'https://www.suburbanpropane.com/locations/phoenix-az/', 'http://www.windycityair.net', 'http://www.lavidamassageshadysidepa.com', None, None, '1592160519', 'http://www.upandawaylandscaping.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, None, 'http://www.sincerelyyogurt.com/locations/peters-township', 'http://www.classickids.biz', 'http://mastercrafttires.com/', 'http://glenwoodacresrvpark.com', 'http://forecloseduponpets.org', 'https://www.mediweightloss.com/locations/scottsdale?_ppc=Z8FWKRXKT5', 'http://galaxiedinerwoodbridge.com', 'http://yeoldsoapmill.com/touch', None, None, 'http://www.1866staydry.com', None, 'http://www.sarphx.com', None, None, None, 'https://homesbyclaudiamarion.kw.com', 'http://cloud9windows.com', 'http://www.bevmo.com', None, None, None, 'http://www.tailgatersilprimo.com', 'http://www.rainbow.travel', 'http://www.timhortons.com/', 'http://www.noblebeastpets.com', None, 'http://compadresmexicanrestaurantwi.business.site', '1592160596', '1592160598', 'http://www.sunnymorning.ca', None, 'https://www.westvalleytech.net', 'http://www.lasvegasbraces.com', 'http://www.cicispizza.com', None, None, 'https://stores.dickssportinggoods.com/az/phoenix/365/', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281360123&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.gamestop.com', None, 'http://www.apple.com/retail/scottsdalequarter/', '1592160628', 'http://www.mark-taylor.com/arizona/san-marquis/?utm_content=visit-website&utm_medium=listing&utm_source=yelp', '1592160634', 'http://www.quiktrip.com/', 'http://www.yellowcheckercabchampaign.com/', 'https://www.lowes.com/store/PA-Monroeville/1660', 'https://megafurnitureusa.com', 'http://greenbeautyspa.com/', 'https://www.wyndhamhotels.com/hotel/52964?tel=18666154223&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52964', 'http://www.itsnewtomeconsignments.com', 'http://www.valueworld.net/', 'http://www.lunarossaristorante.com/', None, 'https://www.bannerhealth.com/locations/mesa/banner-urgent-care-1', None, 'http://www.planetfitness.com/gyms/willowick-oh-985?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://jakesautorepair.com/', None, None, 'http://www.flippnburgers.ca', 'https://camp.nc', 'http://www.lenotrebistro.com', None, 'http://www.yourfloorz.com', None, '1592160693', 'http://www.paradisejuice.com', None, 'http://www.nailsforyou.ca', 'http://www.vintagebymisty.com', None, 'http://www.chezcora.com', 'http://www.thehealthygreek.ca/', 'http://www.upmc.com/locations/hospitals/western-psychiatric/Pages/default.aspx', None, 'https://www.scottsdalecc.com', 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', 'http://www.tccarpetcare.com/', 'http://www.phohongnc.com', 'https://us.louisvuitton.com/eng-us/point-of-sale/usa/louis-vuitton-cleveland-saks?utm_source=yelp&utm_medium=organic&utm_campaign=store_listing_storepage', '1592160727', None, 'http://www.nice1nails.com', None, 'http://www.travelsuitesinn.com', None, 'http://priscillaspantrypetsupplies.business.site', None, None, 'http://www.avidalaserandspa.com/', None, None, 'http://www.city-tavern.com', 'http://www.lockquest.com', None, 'https://www.plannedparenthood.org/health-center/arizona/scottsdale/85251/scottsdale-health-center-2809-90030?utm_campaign=scottsdale-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', None, None, None, None, None, 'http://tirerepairlasvegas.com', 'http://www.tangdynastyurbana.com', None, None, 'http://www.thegridcl.com', None, 'http://www.janasredroom.com', 'http://atrackout.com', None, None, 'http://www.mancavecigarlounge.com', 'http://quicklaneoflasvegas.com/', 'https://locations.theupsstore.com/nv/north-las-vegas/5575-simmons-st?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://consulmex.sre.gob.mx/lasvegas/', 'http://www.azstoragedoctor.com', 'http://www.greenstreetcommunitiesinc.com', 'http://www.pcpropane.com', None, None, "http://charmeck.org/mecklenburg/county/ParkandRec/Greenways/OpenGreenways/Pages/MallardCreekandClark'sCreek.aspx", 'http://www.paradisevalley.edu/', 'http://www.curiouskidspreschoolaz.com/', 'http://www.gardenialanephotography.com', 'http://www.kandrpainting.com', 'http://bestestiedayspa.com', None, None, None, 'https://locations.panerabread.com/oh/hudson/118-w-streetsboro-street.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'https://www.usps.com/', 'http://www.apartmentsnow.online', 'https://www.5280mexicangrub.com', 'http://Destinations.rei.com/Arizona', 'http://www.ferrarimaseratioflasvegas.com', None, 'http://www.justrightlandscape.com', 'https://arizonapain.com/contact-us/chandler/', 'http://www.degnanlawaz.com', '1592160875', None, 'http://azvideomarketing.com', None, 'https://www.marks.com/en/stores/north-york-2625d-weston-road-14-15-crossroads-centre.html', 'http://toterafinefoods.ca', 'http://www.moonhaven.com/', None, 'http://www.torontoguesthouses.com', 'http://massagemaniaglendale.com', None, None, None, None, 'http://www.plannedparenthood.org/health-center/ohio/rocky-river/44116/rocky-river-health-center-2418-91230', None, 'http://www.totaltransit.com', 'https://www.marriott.com/hotels/travel/phxsh-springhill-suites-scottsdale-north/', 'http://www.skatenrd.com', 'https://blueboxmovingcompany.com', 'http://lamsaz.com', 'http://www.designsbylanae.com', None, 'http://arborstownhomes.com', 'http://www.europebound.com/', 'http://www.acehardware.com', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'https://azvent.com/locations/mesa.php', 'http://usacollision.com', None, 'http://www.falloutgames.net', 'http://www.shaanxibiangbiang.com', None, 'http://www.brettbaughman.com', 'http://swgclv.com', 'http://www.kromerradio.com', 'http://www.acmteam.com/acm/outside_home.asp', 'http://www.orvis.com/madison', 'https://www.retreataptsmcalpinecreek.com', None, 'http://www.elvischapel.com', 'http://www.ubreakifix.com/locations/peoria/', None, 'http://www.superchargefoods.com', 'http://www.thesakeexpress.com', None, 'http://www.topnoodle.ca', 'http://www.jazzberryteahouse.com', 'http://www.berkshireplaceapartments.com/', 'http://www.horizonhonorselementary.org', 'https://www.enterprise.com/en/car-rental/locations/us/pa/irwin-4021.html?mcid=iyp:8368400', 'http://www.4colorprint.com', 'https://deserttropicspools.com', 'http://martyscycle.com/', 'https://www.ttc.ca/Subway/Stations/Bay/station.jsp', 'http://www.sunsetgrill.ca', 'http://www.sothlv.com', 'http://www.palms.com/?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.ekgproperties.com', None, None, 'https://www.loandepot.com/branches/las-vegas-nv?sc_camp=DE925F8ECA0F4E0D8092C7E108A615A3', None, 'http://www.newmexicangrill.net', '1592161032', None, None, 'http://www.lenasflowersandgifts.com', 'http://www.cell2fix.com/queen-410-brampton/', None, 'http://www.tonymorenosalon.com', None, None, None, None, 'http://www.callister-law.com', 'http://www.smokeybones.com/', 'http://franklinPhotographyAz.com', '1592161065', 'http://www.thelastwordcharlotte.com/coffee-press', 'http://totalofficenc.com/', None, None, 'https://www.kaltire.com/en/stores/locations/?source=yelp_track&StoreID=864', 'http://www.corinthiapeoples.com', 'http://www.madurbanbees.com/', None, None, '1592161087', 'http://www.petopia.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.BarrowNeuro.org', '1592161101', 'http://www.southpittsburghvet.com', 'http://www.safeguardministorage.biz', 'http://www.lasvegasnvpoolservice.com', None, 'http://www.shopthepig.com', 'https://www.fatburger.com/locations/rancho', 'http://www.preferredparking.com', 'http://charkha.us/', 'http://www.hardboiledinc.com/', 'http://fasttowingaz.com', 'http://www.mephisto.com/us', None, 'https://locator.chase.com/oh/akron/50-s-main-st', 'http://www.lous.ca/', 'http://www.stratospherehotel.com/Food-Drink/Dining/Carvery-108', 'http://onestopnutrition.com', 'https://www.mimiscafe.com/locations/sunset-station/', 'http://www.nice1nails.com', None, '1592161151', None, 'http://diamondcarwash.ca', 'http://delucasplaceinthepark.com', None, 'https://www.torontobuffing.com', 'http://collinscleaners.com', None, 'http://xquiziteaffairz.com', None, 'https://locations.checkers.com/nv/las-vegas/4175-e-desert-inn-rd/?utm_source=Yelp', 'https://www.tedwiens.com', 'http://visionsource-southhills.com', 'http://www.timhortons.com/', 'http://www.arizonaeyedoc.com', None, 'http://www.mrhandyman.com/western-dane-county?sppccampaignid=67352&SPPC=Offline&L=true', 'https://www.whitbylibrary.ca', 'http://www.dangfinerentals.com', None, 'https://pizzariviera.com', 'http://eyetique.com', None, None, 'http://www.haulnassproductions.com/contactus.html', None, 'http://www.kinginklasvegas.com', 'http://www.hartwooddentists.com', 'https://www.ahwfac.com/', 'http://www.southparkoralsurgery.com/', 'http://store-locator.barnesandnoble.com/store/2039', 'http://www.imaginationchildcare.com', 'http://www.palazzo.com/entertainment/shows/baz.html', 'http://www.culturefreshlife.com', None, 'http://lvshotokan.com/', 'http://woolfeye.com', None, 'http://www.cloudadagents.com', 'http://www.viautorepair.info/', None, None, 'http://www.littlecaesars.com', 'http://terros.info', None, 'https://ad.doubleclick.net/ddm/clk/434334113;236814625;y', None, None, 'https://campbellssweets.com/locations/campbells-sweets-factory-ohio-city/', None, 'http://charmeck.org/mecklenburg/county/ParkandRec/Greenways/PlannedGreenways/Pages/McDowellCreekGreenway.aspx', None, None, 'http://www.italianvillagepizza.com/store-locator.html', 'https://locations.jackinthebox.com/us/az/chandler/900-n-cooper-rd', 'http://www.coldstonecreamery.com', None, 'http://www.smileworkscalgary.com', None, 'http://www.bannerhealth.com/locations/phoenix/banner-physical-therapy-mcdowell?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', None, 'https://rosyeyebrowthreading.business.site', 'http://www.sushiichibanchampaign.com', 'http://www.suenosimports.com', 'https://www.wellsfargo.com', '1592161298', None, 'https://www.davey.com/eastpittsburgh?source=Yelp', 'https://www.aria.com/en/restaurants/aria-patisserie.html', 'http://www.dpdough.com', 'http://www.us.allsaints.com/', 'https://www.payless.com/stores-location/OH-PARMA-6259.html', None, None, None, 'https://www.chick-fil-a.com/scottsdale101', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://thenakedbbq.com', 'http://www.ensurco.ca', 'https://www.mattressfirm.com/stores/az/scottsdale/mattress-stores-scottsdale-az-85266-6664.html', 'http://www.tenthousandvillages.com', 'http://chatime.com', 'http://www.childcareproviderlasvegas.com', 'http://www.meckabc.com', 'http://storelocator.pepboys.com/pepboys/stores/pittsburgh/library_road_service_center/01425', 'http://www.obskincare.com', None, None, None, 'http://www.valleyacademy.com', 'https://www.freshlandflowers.ca/?srccode=yelp_track', 'https://www.saladmeister.com', 'http://yogalovepgh.com', 'http://www.countyofdane.com/lwrd/parks/lake_farm.aspx', 'https://silvertoncasino.com/dine/dining-in-las-vegas-on-a-budget/', 'http://lasilmosoptical.com', 'https://www.solasalonstudios.com/salon-professional/lainie-schmidt2', 'http://winghartburgers.com/', 'http://www.bobzip.com', 'http://absoluteautoservicelv.com', 'http://tacoskissiphoenix.lunchroomconstructor.website', 'http://www.adelaideclub.com', 'http://www.drrudisill.com', None, None, None, 'http://www.maxandermas.com/locations/333038', 'http://mariannasalterations.com', 'http://www.bossplow.com', 'http://www.liquordepot.ca/?utm_source=Yelp&utm_medium=Online_Listings&utm_content=Location&utm_campaign=LiquorDepot_AB_Q3_July_September_2017', 'http://www.assuranceexteriors.com', None, 'http://www.shell.com', None, 'http://www.table51.com', 'http://www.recreation.gov/recAreaDetails.do?contractCode=NRSO&recAreaId=7&contractCode=131', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.wildpcs.com', 'https://ad.doubleclick.net/ddm/clk/301028788;127996861;v#/Live%20Weekend%20Entertainment', None, 'http://www.reebokcrossfitlibertyvillage.com/', 'http://www.pittsburgh-serenity.com', 'http://www.torontopubliclibrary.ca/detail.jsp?Entt=RDMLIB014&R=LIB014', 'http://dogboneranch.com', 'http://www.cleanjuice.com', 'http://dilworthcoffee.com', 'http://www.rompdogs.com', 'https://www.haircp.com', '1592161456', 'https://www.surlatable.com/browse/storeLocator/storeHome.jsp?storeId=140', '1592161460', 'http://filigreebeds.com', 'http://www.colonyamerican.com/?utm_source=Yelp!%20Regional&utm_medium=Text%20Link&utm_campaign=Yelp!%20Charlotte', None, 'http://www.juicebaratlvac.com', 'https://canyoncreekrestaurant.ca/vaughan/', None, None, None, None, None, 'http://www.acehardware.com/store-details/09471', 'http://www.timhortons.com/', 'http://www.barrospizza.com', '1592161494', 'http://smokeworldtempe.com', 'http://www.bestdoggonebookkeeping.com', 'http://www.banfield.com/veterinarians/az/phoenix/pho?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://alphaomegafg.com/', 'https://www.enterprise.ca/en/car-rental/locations/canada/on/north-toronto-eglington-yonge-c245.html?mcid=iyp:8368400', 'https://www.aqua-tots.com/surprise', 'http://www.kortmaninc.com', None, 'http://browsthreadingsalons.com', 'http://www.strideawayequestriancenter.com', 'http://www.mattressfirm.com/', None, None, None, 'http://www.saigonphocuisine.com', 'http://www.salvationoutdoor.com', 'http://us.christianlouboutin.com/us_en/', None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', 'http://edhardyshop.com', 'http://www.parkshairhaven.com', None, 'http://www.hautechixvegas.com', 'http://integrity.helpusell.com', 'https://www.avis.com/en/locations/us/nv/las-vegas/qn4', 'http://www.matabar.ca', 'http://www.vivaldisalonsuites.com', 'http://ritzfurnitureplanet.ca/', 'http://movingteamsix.com', None, None, 'http://www.ecocleaners.ca/', 'https://locations.wendys.com/united-states/oh/parma/6970-ridge-road', 'https://www.discounttire.com/store/az/mesa/s/1294?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://biltmorenailbar.com', '1592161583', None, None, 'http://rumerzpgh.com/', 'http://www.suite114.ca', 'http://www.myspace.com/giant45', None, None, 'https://www.homedepot.com/l/Peoria/AZ/Peoria/85345/453?cm_mmc=seo-yelp&', None, None, '1592161607', None, 'https://www.k9viplv.com', 'https://www.hockeyworld.com/index/page/store_details/store_id/10', 'http://www.peninsulaluggageonline.com', 'https://www.phoeniciangaragedoorandrepair.com', 'http://www.LuminosityWellnessCenter.com', None, 'http://www.easternpodiatry.com', 'http://www.peppersfreshmarket.com', 'http://www.tremontscoops.com', 'https://local.albertsons.com/az/mesa/2727-n-power-rd.html', None, 'http://moviescoop.com', 'http://waikikigoldsilver.com', 'http://applefactory.com', 'http://www.brustersicecream.com', 'http://bigjohnspizza.ca', None, None, '1592161649', None, 'http://www.bigboy.com/', 'https://www.bluemercury.com/?utm_source=2016-Yelp&utm_medium=social&utm_content=49&utm_campaign=general', '1592161660', 'http://www.heritageatdeervalley.com', 'http://www.cellaxys.com', 'https://ireh-salon.business.site', 'http://noblecleaners.vegas', 'http://www.tuesdaymorning.com', 'http://specsonbloor.ca', 'http://www.estheticsbycristina.ca/', 'http://www.silkmanlawfirm.com', 'http://hubcapannielasvegas.com', None, None, 'http://www.eastcalgaryregistry.com', 'http://local.firestonecompleteautocare.com/ohio/akron/1245-firestone-pkwy/?lw_cmp=IYP_YPC_MLP_2046', 'http://www.fallsicecream.com', 'http://www.revitasize.ca/', 'http://www.elitefitnesstrainingandcoaching.com/', None, None, 'http://www.atozmovinganddriving.com', None, None, None, 'http://www.lagravineseappraisals.com', 'http://www.custombuiltpizza.com/', 'http://www.jeanvegetariankitchen.ca', '1592161722', 'http://beautyinvegas.com', 'http://www.countyofdane.com/lwrd/parks/indian_lake.aspx', 'http://www.phillipscliniclv.com', 'https://www.mattressfirm.com/stores/oh/streetsboro/mattress-stores-streetsboro-oh-44241-7782.html', 'http://www.hollywoodtans.com', 'http://budget.com', 'http://www.saltcreekofficefurniture.com', 'http://www.happycampersdental.com', None, None, 'http://www.pizzanova.com/locations/mississauga.html', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, 'http://h1racing.com', 'http://pdqmechanicalllc.com', 'http://www.edenwellnessvibration.com', 'http://yardbusterslandscaping.com', None, None, 'http://www.uwhealth.org/locations/detail.jsp?locationId=254', None, None, 'https://www.backfithealth.com', None, 'http://microsoft.com/en-ca/store/locations/ab/calgary/chinook-centre/store-1053?pointit_retailsustain_sitelinks_Yelp', 'http://ruggedmoosedecor.com', None, 'http://simplekitchento.com', 'https://www.republicservices.com?utm_source=yelp.com&utm_medium=referral&utm_campaign=Yelp_Profile_Click&utm_term=gTepcuWPpm5jqrVjM0gwew', 'https://www.standardplumbing.com/locations/PE', 'https://local.fedex.com/az/phoenix/office-5048/', '1592163820', None, None, 'https://ollyshoes.ca/pages/yonge-street-store', 'http://www.waterfrontoronto.ca/explore_projects2/west_don_lands/don_river_park', 'http://www.biggamblesrummagesale.com', None, None, None, None, 'http://www.arizonabouncearound.com', 'http://lavidamassageballantynenc.com', None, 'http://adultmart.com?utm_source=yelp&utm_medium=social&utm_campaign=yelptest&utm_content=url', 'http://www.firewatercalgary.com/', 'https://www.hertz.com/rentacar/location/unitedstates/arizona/phoenix/PHXC04', 'http://www.sameatshops.ca', 'http://mywheelguylv.com', 'https://locations.theupsstore.com/az/tempe/1753-e-broadway?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'http://www.shopsteelcity.com', 'http://www.RiteRug.com', 'http://www.thegolfdome.com', 'http://hianddrycleveland.com', 'https://plan.dignitymemorial.com/yp/plan/?id=542949820&utm_source=yp.com&utm_campaign=ypm&utm_medium=display&utm_term=386&utm_content=mlp', 'http://www.eurogyro.com/', 'http://www.marriott.com/hotels/travel/cltfa-fairfield-inn-and-suites-charlotte-arrowood/', '1592163884', 'http://www.logojoy.com', 'https://locations.theupsstore.com/az/scottsdale/16211-n-scottsdale-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.donttreadonbeans.com', None, None, 'http://www.sleepcountry.ca/', 'http://allcountypet.com', 'http://glenmeadowsauto.mechanicnet.com', 'http://www.parloursalon.com', None, 'http://www.merchantoftennis.com/', 'http://www.neshoffscarpetcleaning.com', 'http://www.fortmcdowelladventures.com', 'http://www.psychicamandamarquez.com', 'http://www.tricountymg.com', 'https://www.alaschools.org/arizona/az-schools/gilbert-k-6', None, 'https://pastureandplenty.com', 'https://palacestation.sclv.com/Gaming/Bingo?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', None, 'http://www.cupidstoybox.com', None, 'http://thesanddollarlv.com', 'http://www.usysnv.net/page/show/110658-bettye-wilson-soccer-complex', 'http://www.themeadowsschool.org', None, 'https://www.esso.ca/en/gas-station/richmondhill-on-beavercreekesso-200302403', 'http://www.studiocsalonsaz.com/studio-c', 'http://www.clorebeauty.com', '1592163956', 'http://klimateking.com/', 'http://www.spinco.ca', 'http://infinitevapor.com', '1592163966', 'http://www.thebrewteabar.com', 'http://www.chopchopchinesekitchen.com', 'http://www.chilitos.ca', 'http://thewienerscirclelv.com/', 'http://www.hob-nobs.com/', 'http://www.legendaryhomeservice.com', 'http://DefiantPestControl.com', 'https://www.napoli.vegas', 'http://www.brunswickkidds.com', 'http://www.ctrca.com/', 'https://www.trekbikes.com/us/en_US/retail/madison_west/', 'http://www.streetsofnewyork.com', 'http://nbdmd.com/', 'http://phoenix.gov', 'http://www.azpodiatrists.com', 'http://www.larryscocktails.com', 'http://www.cookout.com', 'http://spandexcity.com', 'http://www.casalinochiropractic.com', None, 'http://www.samdaebbq.com', 'http://balancingpawsdogtraining.com', None, '1592164037', 'http://www.revivme.com/las-vegas?utm_source=yelp-org&utm_medium=webclicks', '1592164042', 'http://www.beelogicpestcontrol.com', 'http://www.creativestyleslv.com', None, 'http://Www.bellaskinsalon.com', 'https://www.chick-fil-a.com/rossparkmall', '1592164058', None, 'http://www.bluejadechinese.com', 'http://nswhobgyn.com', 'http://brewsters.ca/', '1592164073', 'http://www.luxebrides.vegas', None, None, 'http://paradisebakery.com', None, 'http://actoneyouththeater.org', 'http://www.cityofhenderson.com/henderson-happenings/facilities/overview-of-pools/pool-locations/whitney-ranch-indoor-pool', 'http://www.7-eleven.com/?yelp=29384', 'http://www.johnniewalkerrv.com/index.php', 'http://www.ColleenSellsAZ.com', None, None, 'https://www.haircutmengibsoniapa.com', 'https://www.payless.com/stores-location/IL-CHAMPAIGN-5067.html', '1592164114', 'https://www.cafetempeaz.com', None, None, 'http://www.bartongrouphomesearch.com', 'http://foleysac.com', 'http://www.foodandwineexpo.ca/sitepages/', None, None, '1592164141', None, 'http://www.jaginchystuff.com', 'http://www.tremontpointe.com', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282975319&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.qashtonbeauty.com', 'http://www.phoenixairport.hilton.com', 'http://www.sweetaffairsbakeshop.com', 'https://www.verizon.com/home/storelocator/pa/pittsburgh-15206/', '1592164167', None, 'http://local.firestonecompleteautocare.com/arizona/peoria/10661-n-84th-ave/?lw_cmp=IYP_YPC_MLP_11932', None, 'http://www.azcoolmotors.com', 'http://www.shoproka.com/web/', 'http://www.gostorageone.com/self_storage/North_Las_Vegas/zip_89084/storageone_self_storage/10487', 'https://www.anytimefitness.com/gyms/1820/Markham-ON-L6B-0P2/?utm_source=yelp&utm_medium=local', 'http://www.pinkpolishnailspa.com', None, None, 'http://www.boyacklawgroup.com', 'http://dekra.us/en/nevada/las-vegas-3209-n-rainbow-blvd/', 'http://www.goplaycanada.com', 'http://www.crispfoods.com', 'http://www.restechservices.net', 'http://www.polepositionraceway.com', '1592164211', None, 'http://geraldinetoronto.com/', 'http://www.bakerperformingarts.com', 'https://dutchbros.com/?utm_source=las-vegas&utm_medium=yelp&utm_campaign=website_las-vegas', None, None, None, 'https://tortillafeliz.com', 'http://www.charlotterecyclery.org', 'http://www.maxmoving.ca', None, 'http://www.daggerdiesel.ca', 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/beachwood-fhsc', None, 'http://www.cannonpharmacies.com', 'http://www.bettysonking.com/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.waffluv.com/find-us', 'http://www.dunkindonuts.com', 'http://www.ytr.com', 'http://www.scoopnswirl.com', 'http://www.piedmont-eyecare.com', 'http://www.thefoodconnectionlv.com', None, 'http://www.starbucks.com/', 'http://www.copperrestaurant.com', None, 'http://www.peachykleenlaundry.com', 'https://wildfire.sclv.com/Wildfires/Wildfire-Rancho?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://extremepita.com', None, 'http://www.axelmortgage.com', 'http://www.hobbylobby.com/StoreLocator/Search?Latitude=33.2774819&Longitude=-111.73165570000003&SearchOn=85297&SearchDistance=50', None, None, None, 'http://www.myerstar.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', '1592164296', 'http://www.sportclips.com/', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282975058&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, '1592164307', 'http://www.busterstransmission.com', 'http://www.the-alley.ca', 'http://www.mifamiliamexicanfood.com', 'http://Www.thebubblegumgallery.vpweb.com', None, None, 'http://www.lincolnlandexpress.com/index.php', 'http://www.kaiulanidetailing.com', 'http://restaurants.quiznos.com/oh/lorain/amherst-44053', 'http://www.angelscremationandburial.com/', None, None, None, 'http://www.luxepethotels.com', None, 'http://www.officedepot.com/storelocator/az/chandler/officemax-6515/?cm_mmc=GMB-_-6515-_-Website-_-NS', 'https://www.hughesfloorcovering.com/yelp-offer', 'http://www.pinesatcarolinaplace.com', None, None, 'http://www.charlotteobserver.com', None, 'http://www.tmdish.com', 'http://www.insideoutpatio.ca', 'http://www.firecreekcoffee.com', None, None, 'http://www.QuickKeyLocksmithLasVegas.com', 'http://www.loftea.ca', 'http://sandersonplumbinglv.com', None, 'http://www.sopra.ca', 'http://mylifelinemd.com/', 'http://EUsweets.com', 'https://vinoandcanvas.com', 'http://www.desertsunpeds.com', 'http://www.allstardiscountmuffler.com', '1592164392', None, None, 'http://www.pokerpalace.net/', 'http://www.pizzapros.ca', 'https://www.thebso.com/locations/on/toronto/beauty-supply-outlet-haircuts-11813.html', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_112', 'http://www.salstuscangrill.com/', 'http://www.arizonahikebikeboard.com', 'http://www.providentlawyers.com', None, 'http://www.unicarcollision.com', 'http://kickstandcharlotte.com/', 'http://www.american-self-storage.com/avondale', None, 'http://www.TopScottsdaleHomes.com', 'http://www.ssrealtylv.com', 'http://www.thelimited.com', None, 'http://www.shawarma-palace.com', 'http://www.picturepeople.com/default.aspx?PK=e3adeef4-54b4-43c6-990a-619531e6637b', 'http://www.linsseafoodbuffet.com', None, 'http://www.whichwich.com', 'http://redlinediagnosticsllcauto.com', 'https://www.walmart.com/store/5085/belmont-nc/whats-new', None, 'https://stores.whitehouseblackmarket.com/boutique/white-house-black-market-kierland-commons', 'http://www.theconcordcove.com/', None, 'http://thenailchamber.com', '1592164461', None, 'https://www.paradisegrapevine.com', 'http://www.chrispuhlmanflowersandgifts.com/?srccode=yelp_track', 'http://phbalancedpool.com', 'http://www.timhortons.com', 'http://petemac.com/gilbert/', 'https://millersalehouse.com/locations/henderson/?utm_source=Yelp&utm_campaign=Yelp', 'http://nailing.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://vehbrothers.com', None, None, None, 'http://www.noizeboyz.com', 'http://www.originalchimneys.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.blackhawkcc.com', 'http://www.dollargeneral.com', 'http://kingdom-restaurant.business.site', 'https://www.choicehotels.com/illinois/urbana/comfort-suites-hotels/il366/rates', None, 'http://www.sunburstmusic.com', 'http://torontoauto.autotrader.ca/contact-form.htm', 'http://www.thecleverkoi.com/', 'http://www.madcitypetclinic.com', 'http://www.tandori.ca', 'http://www.waitressworldllc.com', 'http://homeinsulationaz.com', 'http://www.woodworkersemporium.com', None, 'https://www.elnuevotaquito.com', None, None, 'http://luxenailsspaphoenix.com', 'http://www.masakosushibar.ca', 'http://www.pandawokscarborough.com', None, 'http://www.tacobell.com', None, 'https://www.sunbritedental.com', 'http://atticsalt.co', None, None, 'http://www.drfineberg.com', 'http://www.uscryotherapy.com/location/scottsdale-az/', 'http://www.sureshotbilliardsaz.com', 'http://uspizzasurpriseaz.com', 'https://www.statefarm.com/agent/US/NC/Charlotte/Jack-English-YKJTS2RZ000?cmpid=M8V7_BLM_0006', None, 'http://www.bedbathandbeyond.com', 'http://www.arizonaministers.com', 'http://www.usairways.com?c=maplisting_Yelp_21041', 'http://www.arbys.com', 'http://www.kuohua.com', 'https://brighthomeenergy.com', None, 'https://www.meineke.com/locations/pa/monroeville-512/?utm_source=yelp&utm_medium=xvc', None, '1592164595', None, '1592164600', 'http://www.shoelessjoes.ca', 'http://azsportsmedicine.com', 'http://www.decadentdesserts.ca', '1592164609', 'http://www.whynotpizzaclt.com', None, 'http://www.diventures.com', 'http://www.ncix.com/', '1592164621', None, None, None, None, 'http://locations.michaels.com/oh/avon/1532/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.allamericanmodernsportsgrill.com', 'https://www.windsorstore.com/blogs/store-locator/az-scottsdale-scottsdale-fashion-square', 'http://www.trumphotels.com/las-vegas', 'http://www.grldcheese.com', 'http://www.wowwash.com', 'http://www.zoyogurt.com/arcadia/', 'https://hatfieldmedicalgroup.com/red-mountain-primary-care-arizona/', None, 'http://www.lafitness.com/Pages/clubhome.aspx?clubid=669', None, 'http://shop.tuesdaymorning.com/', 'https://www.pizzaville.ca/stores/view/4335-bloor-street-w', 'https://www.meijer.com/shop/en/store/146/?cmpid=OLA:040319:YelpGrocery', None, 'http://local.skechers.com/AZ/GILBERT/237/', None, 'http://www.arbys.com', None, None, 'http://www.gratefulgardens.net', 'http://www.wynnlasvegas.com/Shows', 'http://www.recess.net/', 'https://www.aaautocarelv.com/locations/decatur-blvd/', 'http://www.remnanthealth.com', 'http://computerdocnc.com', None, None, 'http://www.papajohns.com', 'https://bananarepublic.gap.com', 'https://www.boehmerheating.com', 'http://fancynailsnorthlasvegas.com', 'https://www.vibenailbarlv.com', None, 'http://www.littlemountaincc.com', None, 'http://azglaucomaspecialists.com/our-locations/phoenix/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://icedoutbarbershop.com', 'http://www.moxies.ca', 'http://www.villamadina.com', 'https://www.davidyurman.com/stores/s/david-yurman-the-forum-shops-at-caesars?ecid=listing%20marketing%20store%20LasVegas%20all%20082216%20all', 'http://www.coconutsaz.com', 'http://www.superstarcarwashaz.com', None, 'http://naildistribution.com/', 'http://www.bk.com', 'http://www.screenlounge.ca/', 'http://beachpizzavegas.com/', 'http://www.anthropologie.com', 'http://www.comicheaven.com', 'http://www.quiktrip.com', 'http://richardsandoval.com/commissary', 'http://www.coldstonecreamery.com/stores/20030', None, 'http://lvbraces.com', 'http://www.silverspoonphoenix.com', 'http://www.ashleyfreehan.com', 'https://radiantdivine.com', 'http://www.dahmensathawks.com', 'http://www.kidsu.ca/', 'https://culinaryhc.com', None, None, 'http://www.luckybreakaz.com', 'http://www.3dudesquilting.com', 'http://www.theprincessmargaret.ca/en/pages/default.aspx', None, None, 'http://www.estrellamountain.edu/', 'http://www.greendrycleaning.ca', 'http://www.westshorehome.com', 'http://www.greatclips.com', None, 'http://laurel-md.yellowusa.com/', 'http://www.honestjohnspgh.com', None, 'http://www.tandoorichaska.com', 'https://www.tempemoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', None, 'http://myporcellis.com', None, 'http://www.JimmyJohns.com', None, 'https://www.godsgardentreasures.com', None, None, 'http://www.burns-scalo.com', 'http://www.mrsteamcarwash.ca', None, 'http://www.nouvellemariaspa.com/', 'http://rinckerlaw.com', 'http://www.drchemdry.com', 'http://nationsfreshfoods.ca', 'https://www.kohls.com/stores/nv/lasvegas-1372.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.fourpeaksrentals.com', 'http://www.canuckamusements.com', 'https://greenvalleyranch.sclv.com/Dining/Hanks?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://stores.sportsauthority.com/az/phoenix/sporting-goods-phoenix-692.html', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZGS', 'https://stores.bestbuy.com/nv/las-vegas/6950-arroyo-crossing-pkwy-1044.html/?loc=ns100&ref=NS', '1592164907', 'http://www.roccuzzorealty.com', 'http://www.surprisechildcare.com', 'http://www.shuttlersuniform.com', None, 'http://www.ecochoicewindows.ca', 'http://www.sushiandrolls.ca', None, 'http://www.backofhouse.ca/', 'http://www.handmunlimited.com', None, None, 'http://www.asimpleaffairlv.com', 'http://www.kegsteakhouse.com/en/locations/ON/toronto/mansion-keg/', 'http://www.spinellikia.com', 'http://www.saborcharlotte.com', 'http://www.kctowinginc.net/', 'https://www.crudowine.com', 'https://www1.shoppersdrugmart.ca', 'http://www.jaipurgrill.com', None, 'http://madisoneyecare.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.blackbearcharlotte.com/', 'http://mycupoftea.ca', '1592164974', None, 'http://olympiclimoservice.ca', 'http://www.beddingtons.com', 'http://villagecp.com', None, None, 'http://www.aonefingerprinting.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.66054.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:66054', 'http://elementsdrycleaner.com/', 'http://www.hungfooktong.ca', 'http://www.ayscater.com', '1592165005', None, 'http://www.mwuclinics.com', None, None, 'http://amelia-c.com/', 'https://www.hilton.com/en/hotels/pitmcht-home2-suites-pittsburgh-mccandless-pa/?SEO_id=YELP-HT-PITMCHT', 'http://www.dunkindonuts.com', 'http://local.buckle.com/PA/PITTSBURGH/415/', 'http://www.pleasantlakeapartments.com', 'https://www.supercuts.com/locations/az/phoenix/village-square-haircuts-9668.html', '1592165031', 'http://www.ateamair.net', 'http://GoldenRuleFB.com', 'https://locations.jackinthebox.com/us/nv/boulder-city/1101-nevada-hwy', None, 'http://www.greengardenflowers.ca/', None, 'http://local.skechers.com/AZ/GILBERT/237/', None, None, 'http://www.bestbuy.com', 'http://www.drshalupal.com/about.html', 'http://www.downwarddoggrooming.ca', None, 'http://www.exxonmobilstations.com/home.php?c=20140424134755&lang=en-us&storenum=757cfd0e77ee7a4ea34c6a6a556f7058', 'https://www.staples.com', 'http://www.federicosmexicanfood.com/', 'http://www.rainbowchiropracticcenter.com', 'http://www.janefendelman.com', None, 'https://glendaleparts.com', None, '1592165090', 'http://www.hairhappiness.com/ca/index.php', None, 'https://www.walmart.com/store/2112/scottsdale-az/details', 'https://www.druryhotels.com/locations/pittsburgh-pa/drury-plaza-hotel-pittsburgh-downtown', 'https://sincityent.com', 'http://www.bondplace.ca', 'https://allyouneedsmokeshop.com', 'http://www.suntechnc.com', 'http://www.mariepain.com', 'http://lazarbakery.ca', 'http://www.dollargeneral.com', 'http://www.platinumblondestudios.com', None, 'http://Chandlersmilesbrighter.com', None, 'http://www.meritagehomes.com/', None, '1592165136', 'http://fiveguys.com', None, None, None, 'http://www.barbarycoastcasino.com', 'http://abcsanitary.com', 'http://meatmarketvintage.com/', None, 'http://coconutcleaningco.com', None, 'http://bostonmarket.com', 'http://drlaffa.com', 'http://www.davescosmicsubs.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=723&utm_content=bpas', 'http://www.lrlv.com', None, None, 'http://www.bluediamondairductcleaning.com', 'http://www.castelloristorante.com', 'http://bit.ly/103bJzP', 'http://www.usps.com', 'http://aromawcs.ca', 'http://lifeguardsolutionsllc.com', None, 'http://www.chandlermall.com', None, 'http://www.aceretailer.com/aceonwilly/', 'https://reliancehomecomfort.com/toronto/', None, 'http://pizza.dominos.ca/Mississauga-Ontario-10348', None, 'https://www.clearchoice.com/locations/dental-implants-phoenix/?trans_id=webdisyelp&utm_campaign=Yelp&utm_source=YelpListing&utm_medium=Listing', 'http://www.4BCafe.com', 'http://www.onabun.ca', 'https://roxybar.ca', 'http://watchoutaz.com', '1592165236', 'http://www.drglick.com', 'http://licecrew.com', 'http://www.cafecentralclt.com', 'https://www.thebrick.com/pages/store-calgary-sunridge', '1592165249', None, 'http://wolfgangpuck.com/restaurants/casual-dining/wolfgang-puck-express/7730', '1592165258', 'https://www.dsw.ca/en/ca/', 'http://www.studio223az.com', 'https://locations.theupsstore.com/az/phoenix/1934-e-camelback-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.andoverwoodsapts.com/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.7-eleven.com/?yelp=29384', 'http://www.evelinecharles.com/', 'http://www.bffgyms.com', 'http://bbdrybar.com/', 'https://stores.advanceautoparts.com/nc/charlotte/2910-freedom-drive?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', None, 'http://drakids.com', 'http://Www.lasvegaspsychic.com', 'https://www.vegasdeserttours.com', 'https://www.lasikvisioninstitute.com/lasik-eye-surgery/tempe-surgeon-center/?subid=TMP&venid=YLP31', 'http://www.7-eleven.com/?yelp=29384', 'http://www.la-mestiza.com/', None, None, 'http://check-please-cafe.business.site', 'http://www.sweetitis.net', 'http://www.papyrusonline.com/', 'http://cutenailscharlotte.com', 'http://www.drumsnflats.com', 'https://www.uhaaz.com', 'http://www.butlerplaza.net', 'http://www.filibertos.com', None, None, 'http://nynbeauty.com/', 'http://www.tastebudsyogurt.com', '1592165348', 'http://pellathehandyman.webs.com/', 'http://www.azmediquip.com', 'http://www.efilenevada.com/', 'https://himali-kitchen.business.site', None, 'https://gynecarelv.com', None, 'http://www.annschophouse.com', 'http://www.fitnessinmotionlv.com', 'http://wwwtowingwithtlc.wixsite.com/website', 'https://repestservices.com', 'https://www.ulta.com/stores/charlotte-nc-590', None, 'https://local.safeway.com/safeway/az/chandler/4970-s-alma-school-rd.html', 'http://www.dogsbollockspub.com', 'http://www.freshii.com', 'http://www.havencraft.org', 'http://www.ampm.com', 'http://www.rockyrivervineyards.com', 'http://www.gleemhomecleaning.com', 'http://www.peets.com/?cm_mmc=yelp*peets*8_28_12_homepage*na', None, 'http://www.aubreyshouseofroots.com', 'https://steakfrites.ca/fr/restaurants/detail/saint-sauveur/', 'http://www.theartshoppe.com', None, 'https://www.twiceasnicefood.com', 'http://motorlessmotionbicycles.com', 'http://www.bathandbodyworks.com', 'http://www.tayloredphotomemories.com', 'https://www.moes.com/find-a-moes/ohio/mentor/6467?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://bk.com/', 'http://www.marriott.com/hotels/travel/cltsd-springhill-suites-charlotte-uptown/', 'http://www.a1carlinemuffler.ca', None, 'http://www.sharpmyknife.com', None, 'https://www.arizonapartybike.com/scottsdale/', 'http://bradyhendersoninspections.com/', 'https://www.jamba.com/nc/charlotte/charlotte-douglas-int-l-airport-613', None, None, 'https://www.take5oilchange.com/locations/oh/bedfordheights-121/', 'http://www.ullaeyewear.com', None, 'http://www.lunaacupunctureaz.com', 'http://dignityvethospital.com', 'http://bodywaxinglasvegas.com', None, 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpwestorganic', 'http://www.legermainhotels.com/en/torontomls/', 'http://www.realcoolhvac.com/', 'http://www.meckafitness.com', 'http://vitalitybowls.com/locations/las-vegas/', 'http://www.southtrailhyundai.com', None, 'http://www.midas.com/pittsburgh/store.aspx?shopnum=6365&dmanum=688', 'http://www.ttc.ca', 'http://grainger.com/', 'http://www.thelakeshorespa.com', None, None, 'http://www.laurentianlanes.com', 'http://www.Park2300.com', 'https://classicwaterheaters.com', None, None, 'http://carpetcleanertoronto.ca', 'http://www.charlesalexanderdistribution.com', 'https://www.planetfitness.com/gyms/monroe-nc?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.thnclinic.com', 'http://www.rosenails.ca', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'http://www.jetluxuryresorts.com', 'http://www.arwright.ca', 'http://www.tugawaytowing.com/home.html', 'https://www.ttc.ca/Subway/Stations/Ossington/station.jsp#Schedule_', 'https://tempestoysterbar.com', None, 'http://www.locksmithsmadison.com', 'http://spicensabzi.us', 'http://www.moviesoncentral.com', 'http://www.jamisymonssalon.com/', None, 'http://locations.harristeeter.com/nc/charlotte/205/', None, 'http://www.saloncercone.com', None, 'http://eggsquis.com/fr/restaurants.php?restaurant=lasalle', 'https://www.montecarlo.com/en/restaurants/brand-steakhouse.html', None, None, None, 'http://www.carwashcleveland.com', 'http://sophiainsapphire.com', 'http://russospizza.net/', 'http://www.secondcup.com', 'http://edeninlove.com', 'http://www.rogersrepairservice.com/', 'http://doubletopping.com', 'http://www.charlotteautogroup.com', None, 'http://www.rebelbook.com', 'https://www.anylabtestnow.com/franchises/huntersville-28078', 'http://www.eatnpark.com', 'http://www.doubledoorinn.com', 'http://robertostacoshop.com', 'http://www.spirithalloween.com', 'http://www.marriott.com/hotels/hotel-rooms/yyzmd-courtyard-toronto-mississauga-west/', 'http://www.dunkindonuts.com', 'http://clevelandsteamercleaner.com', None, 'http://oaklandhallinn.com/', 'http://www.starbucks.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.startrekexp.com', None, 'http://us60selfstorage.com', None, None, 'http://www.jensontotalservices.com', 'https://www.olivegarden.com/locations/nv/las-vegas/las-vegas-cheyenne-ave/1363?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:las-vegas-nv-1363_pl:locurl_rd:1274', '1592165677', 'http://305kustomzdesigns.com', 'http://www.arthurmurrayscottsdale.com/', '1592165689', None, 'http://southwestsmilesdental.com/', 'http://www.prestigemusicacademy.com', None, None, None, None, 'https://www.wontonking.com', None, 'http://www.dunkindonuts.com', None, None, 'http://www.notecollection.com', None, None, 'http://rajafoods.ca', 'http://www.phoenixalterations.com', None, 'http://www.insurewithmelissa.com?cmpid=d3u7_blm_0006', 'http://www.cafe-mirage.com', 'http://livingyogacenter.net/', 'http://deserttintlasvegas.com', 'http://www.restoreandreplenish.com', 'http://www.palaciosupholstery.com', 'http://elisabat.com/', 'http://www.yogurttimedt.com', 'http://cityproperty.com', 'http://www.Ricosacai.com', 'http://www.alternativepaths.org', 'http://deerfootmeadowsoptometry.com/seton-optometry-location-and-hours/', None, 'https://thefaceshop.ca/en/pacific-mall-center-32-32-32-32/', 'http://www.silverminesubs.com/', 'http://seasaltbar.com', None, None, 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, 'http://www.menchies.com/frozen-yogurt-shops/frozen-yogurt--northland-plaza-ab', 'http://www.fosdalbakery.com', 'http://www.BombHairVegas.com', '1592165799', None, '1592165804', None, 'http://www.justroughinit.com', None, 'https://www.hazukiphotography.com', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://style-encorenorthhills.com', 'http://matchacafemaikoclt.com', 'http://Hydra-tattoo.com', 'http://www.sunautoservice.com/auto-repair/nv/las-vegas/las-vegas-tropicana-52', None, 'http://www.chura-hair.com', 'http://www.spoiledchics.com', 'http://www.docwalters.com', 'http://www.sushionbloor.com/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.litehouse.com', '1592165859', 'http://www.specializedflooringaz.com/', None, None, None, 'http://www.crywolfclothing.com', 'http://www.disantoimmigrationlaw.com', None, 'http://www.rossstores.com', 'http://www.popuppizzalv.com', 'http://www.thomaseyecare.org', None, 'https://budgetblinds.com/DowntownPittsburgh/?utm_source=yelp&utm_medium=naf-listing&utm_campaign=NAF-LOCAL-YELP', None, 'https://www.hankinsplasticsurgery.com', None, None, None, 'http://www.spirithalloween.com', 'http://www.heersmanagement.com/properties/property/desert-point-apartments', 'https://www.hilton.com/en/hotels/cltephf-hilton-charlotte-executive-park/?SEO_id=YELP-HI-CLTEPHF', 'https://www.foodandthingsliquoranddeli.com', 'https://www.hairclub.com/locations/on/toronto/hair-loss-clinic-242/?pub=loclisting&utm_source=yext&utm_medium=loclisting&utm_campaign=YX_242', 'http://tubbystubs.com', None, None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://www.dipsidoo.com', 'https://www.annaksalon.com', 'https://www.republicservices.com?utm_source=yelp.com&utm_medium=referral&utm_campaign=Yelp_Profile_Click&utm_term=a7viRDrdChmaTJUqBxg4EQ', 'http://www.urbanairgoodyear.com', 'http://ajsalterations.com', 'http://www.nevadacleanup.com', 'http://qdoba.com', 'http://www.purplepenguinsnow.com/', 'https://www.vietbeautysupply.com', 'http://www.nashvillenorth.ca/', None, None, None, 'http://www.lauerrealtygroup.com', 'http://tpmlasvegas.com', 'http://www.clerebar.com', None, None, None, 'https://www.elizabethtatelaw.com', 'http://www.elegancehaircare.com', None, None, 'http://yourspacesalons.ca/tonyc', 'http://www.greatclips.com/salons/3065', None, 'http://www.cherokeehillsgolf.com/restaurant', 'http://www.housetohomeinspection.com/', 'http://prairiefirechampaign.com/', None, None, 'http://cervantesrestaurant.com/', 'https://www.doanrestoration.com', 'http://www.tjbakerconst.com', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.lasvegasartificialgrass.com/', None, None, '1592166030', None, None, 'http://www.sonobello.com/locations/cleveland/?utm_source=yelp&utm_medium=site&utm_campaign=yelp_loc_page_url', None, None, None, None, None, 'https://www.kitchenstuffplus.com/storelocator/#kspST020', 'http://punjabibynature.ca/home.html', 'https://www.charlottefoot.com', '1592166055', 'http://www.kentlanes.com', 'http://www.pghtacotruck.com', 'http://www.tiltonlmt.wixsite.com/mysite', 'http://www.ghadirmeatmarket.com', 'http://www.starbucks.com/store/15887/', 'http://www.pizzanova.com', None, 'http://actionjacksfurniture.com/', 'http://taylorandcolt.com/commerce-court-toronto/', None, 'http://www.blindstogo.com/en/stores/east-mississauga?ua=L4X+1M1&rds=25', '1592166085', 'http://www.menchies.ca/frozen-yogurt-shops/frozen-yogurt-creekside-crossing-ab', 'https://www.searshomeservices.com/locations/appliance-repair/nv-las-vegas/4000-meadows-lane', 'http://www.sundeviltrophy.com/', None, '1592166100', 'http://www.lakeshorepediatric.com', None, 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'http://www.popularlube.ca', 'https://www.southhillspetresort.net', None, 'http://www.plumbperformingartscenter.com/', 'https://www.vaqueroscarneasada.com', 'http://www.giantlasvegas.com', None, 'http://www.richsrestaurant.com/', 'https://riosecco.com', None, None, 'https://www.ritasfranchises.com/Brodheadsville', 'http://www.drivingtoindependence.com/', 'http://www.piazzamanna.com', 'http://www.lcbo.com', 'http://www.wxdx.com/main.html', 'http://thebelsize.pub', 'http://www.bannerhealth.com/locations/gilbert/banner-physical-therapy-gateway?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', 'http://www.caromonthealth.org/Locations/Hospitals/CaroMont-Regional-Medical-Center.aspx', 'http://tigerlily.com', 'https://www.mielesitalian.com', None, 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', None, 'http://www.peaceofmindandbodymassage.com', 'https://www.eatnpark.com', 'http://scarletdoorcafe.com', 'https://stores.maccosmetics.com/us/nv/las-vegas/3200-s-las-vegas-blvd', 'http://www.dominos.com', 'http://www.vinylwraptoronto.com', 'http://www.brillorestoration.com', None, 'http://www.dunkindonuts.com', None, '1592166203', 'https://www.ediblearrangements.com', 'http://www.ecosmartpros.com/', 'http://www.accurateautoglass.net', 'http://jennysalterations.wordpress.com/', 'http://www.whiskersandpawsvet.com', 'http://happyfeetnailsspa.com', 'http://www.stonefamilyservices.com', None, 'http://www.animalhospitalatgrayhawk.com', 'http://www.restaurantsawadee.com/', 'http://toronto.thepint.ca', None, 'http://cutie-giftshop.business.site', 'http://signaturebarbershop.net', 'http://cuyahogalibrary.org/', 'https://www.wellsfargo.com', None, None, 'http://mrniceguygames.wpengine.com/contact-us/', 'http://www.dunkindonuts.com', 'http://fiveguys.com/', 'http://www.papajohns.com/', None, 'http://www.sonicdrivein.com/', 'http://602autosports.com/', 'http://www.salonescapeaz.com', 'http://www.rocklobster.com.php53-12.ord1-1.websitetestlink.com/ossington/', 'https://www.4wheelparts.com/stores/north-carolina/4wp-charlotte-nc-54', 'https://www.petsmart.com/stores/us/az/phoenix-store0131.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://www.daango.com', 'http://restaurantspago.com', None, None, 'https://www.amr.net/home/lasvegas', 'http://www.hennashoppe.com', None, 'http://www.lickshomeburgers.com', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'https://www.pizza73.com', 'http://www.cigna.com/cmgaz/locations/stapley-multi-specialty-center', 'http://tempeimportsaz.com', 'http://www.restaurant-divino.com/accueil', None, 'http://www.big5sportinggoods.com', None, 'http://www.idoupdolasvegas.com', 'http://www.westlibertyanimalhospital.com', None, None, 'http://www.anteloelectric.com', 'http://www.happyhomeservicesaz.com', 'https://www.upmc.com/locations/community/south-side', None, None, 'http://www.newhighend.com', None, 'http://www.Visionworks.com', 'http://patio-pleasures.com/', None, 'https://www.unlv.edu/donnabeamgallery', 'http://www.virtualworldmadison.com', 'https://www.autozone.com/locations/az/phoenix/3908-e-thomas-rd.html', None, None, 'http://desertwestobgyn.com', 'https://www.twistedmindssmokeshop.com', 'http://www.PalmLane.ca', None, 'https://www.sportchek.ca', None, 'http://www.mezzaninehair.com', 'https://www.fatfreddyscatering.com', 'http://www.asepestandweedsupplies.com', 'https://www.ihg.com/holidayinnexpress/hotels/us/en/rantoul/cmirt/hoteldetail', None, None, 'http://www.babassupperclub.com', 'http://www.champagnestrands.com', 'http://www.boulevardvegas.com', '1592166417', 'http://bloomcigar.com', 'http://extensionroom.com', 'https://www.fascinations.net', 'http://www.theskullzsalon.com', None, 'http://www.indianpunjabibazaar.ca', 'https://www.bobevans.com/our-restaurants/locations/22?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', None, 'http://bestasianmassagelv.com', 'https://locations.davidstea.com/ab-calgary-111', 'http://www.papajohns.com', None, 'https://local.fedex.com/nv/las-vegas/office-1441/', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEWI', 'http://www.vivintsmarthomesecuritycalgary.com', None, 'https://www.terravita.com/neighborhood', None, '1592166467', None, 'http://www.kelseys.ca/', 'http://ago.ca/ago-bistro', '1592166475', None, 'http://www.cbcautism.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'https://www.circlek.com/store-locator/us/tolleson/11450-w-southern/2701130', None, 'http://www.simpleaz.com', None, '1592166498', 'https://scottsdaleearnoseandthroat.com/about-us/meet-our-team/cheryl-a-mackechnie-md', '1592166505', 'http://www.lvcabs.com', None, 'https://hpautorepair.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FPHXPC', 'https://www.purebarre.com/location/san-tan-village-az', 'http://www.canadapost.ca/cpotools/apps/fpo/personal/findPostOfficeDetailPrint?outletId=0000104239', 'http://www.onlinetickets.com/', 'http://www.cwpress.com/', 'http://thesaucebse.com', 'http://www.caferio.com/', None, None, 'http://www.heldtlumber.com', '1592166545', 'https://www.afw.com/stores/az/glendale', 'http://www.tenniswerx.com', 'https://www.publicstorage.com/north-carolina/self-storage-waxhaw-nc/28173-self-storage/2073?pid=wyelp&CID=1245&CHID=AFL', 'https://www.autozone.com/locations/az/phoenix/3908-e-thomas-rd.html', 'http://www.purcelltire.com/retail/retail-locations.aspx?store=85', None, None, 'http://www.envynailspaclt.com', None, 'http://www.organicgarage.com', 'http://abbottcourtesyplumbing.com', None, 'http://www.americanrealtylv.com', 'http://www.angelosohio.com/', 'http://www.sipcoffeeandbeer.com', None, 'http://www.osteriausa.com', None, 'http://www.homegoods.com', 'http://www.vegas-asian-massage.com/', 'http://www.cristinahindslaw.com/', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.shangrilabanquet.com', 'http://japanesespecialties.blog.fc2.com/', 'http://www.gordonbiersch.com', 'http://www.awildhairaz.com', 'http://www.switchbladesalon.com', 'https://www.dairyqueen.com/us-en/locator/Detail/?store-id=5175&localechange=1', 'http://www.theloreleiboutique.com', 'http://www.chandleraz.gov/tumbleweed', 'http://www.pizzahut.com/', None, 'http://www.harrisonlawaz.com', 'https://www.menswearhouse.com/store-locator/2513?utm_source=yelp&utm_medium=listing&utm_content=2513&utm_campaign=AZ', 'http://palacenaillounge.net', None, 'http://www.falconlandscapes.com', 'http://www.trueharmonywellness.com', 'http://lodgecharlotte.com', None, 'http://www.moonflightcoffee.com', 'http://subamanautocare.com', 'http://www.theotheroomlv.com', None, None, 'https://tannertileandstone.com', 'http://rebathandkitchens.com', 'https://www.target.com/sl/mccandless/1218', None, 'https://jamboree-bagel.business.site', None, None, 'https://www.arrowheadccaz.com', None, 'http://floydsbarbershop.net/', 'http://www.livemagnoliaterrace.com', None, 'http://www.oasisspasalon.com', 'https://www.homedepot.com/l/Bethel-Park/PA/Bethel-Park/15102/4176?cm_mmc=seo-yelp&', 'http://www.platosclosetcuyahogafalls.com', 'http://www.quesada.ca', 'http://www.sdsdental.com', 'http://www.ipdiet.com', 'http://www.NEwomensclinic.com', None, None, None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044280216620&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.customcarconcepts.net', None, 'http://www.fabricboutique.com/', 'http://stores.save-a-lot.com/crafton-pa', None, 'http://www.acu-painclinic.com/index.html', 'https://mollymaid.com/southwestern-charlotte-fort-mill-rock-hill', None, 'http://99only.com/store/Mesa---Main/', 'http://www.regaleaz.com/', 'http://www.centennialcollege.ca', 'http://www.carinobistro.ca', 'https://www.ridgeatrobinson.com', 'https://www.integramedical.com', 'https://local.fedex.com/oh/fairlawn/office-1229/', 'http://www.timhortons.com/', 'http://www.graftmadison.com/', 'http://www.arcadiafamilyclinic.com', 'http://www.bayequityhomeloans.com/gilbert', None, None, None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=12197&localechange=1', None, 'http://www.islandpethospital.com', None, None, 'http://www.marshallscanada.ca', 'http://www.tzatziki.ca', None, 'https://www.thejoint.com/arizona/mesa/red-mountain-48026', 'http://www.callcoolaid.com/', None, 'http://www.hoerner.ca', 'http://www.greatlakesoutdoorsupply.com', 'http://www.thefatbelgian.com/', 'http://thailandspamassage.com', None, 'http://www.surgicalweightcontrolcenter.com', None, 'http://www.sonoranorthotrauma.com', None, None, 'http://www.vcahospitals.com/elliot-park/?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Elliot_Park_Animal_Hospital&utm_campaign=main_url', 'http://www.eyebrowsrus.com', 'http://www.herriotts.com', 'http://www.longsontherapy.com', None, None, 'http://www.ardene.com', None, None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.dominicspizzamedina.com', 'http://atrautoglass.com', None, 'http://livingwellhomes.com/apartments/details/escondido_apartments', 'http://www.swisschalet.com', 'http://justincookhomes.com', 'http://octanecf.com/', 'http://www.theladysilvia.com/', 'http://www.whitfillnursery.com/', None, None, 'http://theodorewilliamslaw.com/', 'https://upscalemixologist.com', None, 'http://fancynailsaz.com', 'http://www.vivalasguestlist.com', 'http://www.dwr.com/category/find+a+studio/scottsdale.do?mobile=off', None, 'http://gilbert.donutworryaz.com', 'http://greenleafeinncharlotte.com', 'http://www.ahsappliance.com/', None, 'https://www.villageeastcleaners.com', None, None, 'http://info.lululemon.com/stores/us/las-vegas/fashionshowmall', 'http://www.involtini.ca/', 'http://www.blackforestbooksandtoys.com/', 'http://drjimshipley.com', None, 'http://www.arizonaorganic.com/', 'http://www.jasontheplumberllc.com', None, 'http://www.benfranklinplumbingcharlotte.com', 'http://www.aznypdpizza.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://Geostacos.com', 'https://www.thingsremembered.com', 'http://bikepirates.com/', 'http://manhattanpizza4lv.com', 'http://www.greatclips.com/salons/9261', None, 'http://www.divinedoggies.ca', 'http://www.desertdove.com', 'http://www.LocalMotionPGH.com', 'http://www.shopchristophertodd.com', 'http://www.umamipoke.com', '1592167022', 'http://www.marathon.com', 'http://www.timhortons.com/', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.premiercoachworks.com', None, 'http://swigs.ca', 'https://globalgifts.ca', None, 'http://www.sfxphx.org', None, 'https://www.napaonline.com', None, '1592167056', 'http://directpcc.com/', 'https://www.cricketwireless.com', 'http://www.gotaticket.net', None, None, None, 'http://www.rentalstempe.com', None, 'http://www.costco.ca/warehouse-locations/vaughan-woodbridge-on-547.html', 'http://www.momosushilasvegas.com', 'http://threeamigoscharlotte.com', 'http://www.sincitycomputerservices.com', 'https://www.petahead.ca', None, 'http://www.acropoliscg.com', 'https://www.interdent.com/gentle-dental/locations/az/phoenix/702-e-bell-rd-dentist-office/', 'http://www.foundery.is/', 'http://waxhawdentalcenter.com', 'http://www.trainwithgabe.com', 'http://laplanchagrills.com', None, 'http://eastwestblinds.com/?utm_source=Yelp&utm_medium=Yelp%20CPC&utm_campaign=Yelp%20East%20West%20Blinds', 'http://bespokeinn.com/', 'http://www.dunkindonuts.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.craigrd.com/', None, 'http://www.cash4chaos.com', None, None, 'https://www.autozone.com/locations/az/scottsdale/7401-e-mcdowell-rd.html', 'http://www.acebartending.com', 'https://www.target.com/sl/las-vegas-blue-diamond/2164', 'http://newbeginningscounselingcenters.com', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://stockmanos.com', None, None, 'http://www.blingtour.com', 'http://charlotteswim.com/', 'http://www.chiro-phoenix.com', None, 'http://alterios.webs.com/', 'http://azteccaraudio.com', 'http://www.arizonaveterinaryoncology.com', 'http://www.robertcoomergroup.com', None, 'http://www.portofsubs.com', 'http://gastondentalassociates.com/', 'http://www.aapglv.com', 'http://www.practiceofpositivity.com', 'https://hirehometeam.com', 'https://www.kohls.com/stores/nv/henderson-667.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.hillsideappliancerepair.com', 'http://www.lorain.lib.oh.us', 'http://www.dunkindonuts.com', None, 'http://www.Konbeasushi.com', 'https://www.walmart.com/store/1598/phoenix-az/whats-new', 'http://www.agaveyaguacate.blogspot.com/', 'http://www.periodentalimplant.com', 'http://www.nandos.ca/restaurants/calgary-17th-coming-soon', 'https://www.signaturestyle.com/locations/on/richmond-hill/first-choice-haircutters-51417.html', 'http://aproposcreations.com/', 'http://www.theshopprinting.com', 'http://fritesstreet.com/', 'http://www.cyanimalclinic.com', 'http://mrsouvlaki.ca/en/locations/ontario/hudson%E2%80%99s-bay-centre.html', None, 'http://local.buckle.com/OH/WESTLAKE/419/?utm_source=Buckle&utm_medium=Website&utm_campaign=Store+Locator', None, 'http://www.starbucks.com/store/9334/', None, 'http://rebeltoronto.com', 'http://mikasgreek.com', None, 'http://www.premiumgranite.com', '1592167276', 'http://pouloslawfirm.com', None, None, None, 'https://andersondentalaz.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.devicepitstop.com', 'http://www.keungsrestaurant.com', None, 'https://www.chickasawdemolition.com', None, 'http://washmeohio.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://Lasajspa.com', 'http://transnationalmoving.com', None, 'http://www.pinkberry.com', 'http://www.paradiseflowermarket.net', None, None, 'http://spamontst-hilaire.com', 'http://www.aamco.com/centerinfo.asp?centerNum=4128569500', None, 'http://www.banfield.com/veterinarians/nc/cornelius/coe?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, None, 'http://www.wbt.com', 'http://tanakasmartialartslasvegas.com', None, 'http://www.arrowprofessionals.com', 'http://www.princetonclubxpress.net/', 'http://www.parkersdowntown.com', '1592167562', None, None, None, None, 'http://www.hibachigrillphoenix.com', None, 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', '1592167582', 'http://www.theartshoppe.com', 'http://www.stjohnsmusic.com/locations/calgary', None, None, None, 'http://www.spanishtrailcc.com', None, 'https://www.kruyerdental.com', None, 'http://www.fellinislv.com', '1592167611', 'http://sincitybrewtours.com', None, '1592167616', None, 'http://www.caseysdrafthouse.com', None, 'http://www.tradesecrets.ca/', None, 'http://otrocafe.com', 'http://www.lvnailspanv.com', 'http://www.letseat.at/paparazzipizzeria#home', None, None, 'http://lapaloma.ca/about-us/', '1592167648', 'http://www.healthyplanetcanada.com', None, None, None, 'https://www.aplaceformom.com/assisted-living/arizona/phoenix', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592167664', 'http://www.Kaizensushi.ca', None, 'http://helpinghandhandymanservice.com/handyman-services/', None, 'http://www.furniturebank.org', 'http://www.verizonwireless.com/', 'http://www.buddhabodyyoga.ca', None, None, None, 'https://www.rodiziogrill.com/henderson-nv/', 'http://www.sunridgemazda.com', None, 'http://www.breastforbaby.com', 'http://www.bowlingdynamics.com/', 'https://www.americanrealtyacademy.com', 'https://www.ashleycourt-apartments.com', None, 'http://www.lasvegashairandmakeup.com', None, None, 'http://www.campbowwow.com/summerlin', 'https://centennialhillsrealty.managebuilding.com/Resident/PublicPages/Home.aspx', 'https://www.anytimefitness.com/gyms/2194/Cottage-Grove-OR-97424/?utm_source=yelp&utm_medium=local', None, 'http://www.glickdental.com/', 'http://Lawdawgtrailtours.com', 'http://www.citymarketdeli.com', None, 'http://www.regalnails.com', 'http://www.tipitytoenails.com', 'https://www.foodforthought.ca/contact-us/markham', 'http://www.salonlola.net', None, None, 'https://www.publicstorage.com/arizona/self-storage-phoenix-az/85027-self-storage/1113?pid=wyelp&CID=1245&CHID=AFL', None, None, None, 'https://bridalxoxo.com', 'http://www.statewidelightinglasvegas.com', 'https://www.enterprise.com/en/car-rental/locations/us/oh/mentor-3921.html?mcid=iyp:8368400', 'http://www.cozinedental.com', 'http://www.lessermeansmore.com', 'http://www.drinkbambu.com', None, 'http://www.villaserenahenderson.com', None, '1592167790', 'http://www.sevencalgary.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.hilton.com/en/hotels/cltsohw-homewood-suites-charlotte-southpark/?SEO_id=YELP-HW-CLTSOHW', None, 'https://www.menswearhouse.com/store-locator/2503?utm_source=yelp&utm_medium=listing&utm_content=2503&utm_campaign=AZ', 'http://www.eastwestbank.com', 'https://stores.godiva.com/us/nv/las-vegas/3200-las-vegas-blvd-s.html', None, 'http://www.fracturedprune.com/location_charlotte.php', 'http://www.arizonapoolpros.com', 'http://www.kleinhenzjewelers.com', None, 'http://www.eastvalleypetdoors.com', 'http://www.chatpattachowk.ca', None, 'https://www.bostondentalgroup.com/locations/happy-dental-west-valley/', 'http://www.dasonii.com', 'http://gourmetschnitzelhouse.com/', 'https://www.kohls.com/stores/pa/monroeville-289.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.parasitetesting.com', 'http://www.picnicfood.ca', 'http://counseling.healingcouples.org', 'http://www.ssrtowing.com/', None, '1592167861', 'http://www.Vegasjj.com', 'http://www.jerianchiropractic.com', None, 'https://www.sprint.com/storefronts/bd/sprint-chandler-az-85226-fcs-1172/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.starbucks.com', 'http://fitnesstogether.com/waxhaw?utm_source=Yelp%20Web&utm_medium=Yelp%20Web&utm_campaign=Yelp%20Web', 'https://www.carefreecoverings.com/home', None, 'https://www.sunsetgrill.ca', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://arizonareptilecenter.co/', 'http://www.tastidlite.com/', None, None, 'http://www.victoriassecret.com', 'http://www.arrowoodmed.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.indiascafeandkitchen.com', None, 'http://www.dollartree.com', 'http://www.soshandyman.ca', 'http://www.greencleanphoenix.com/', None, None, None, 'http://paninisgrill.com/locations/euclid', None, 'http://www.cellxperts.ca', 'http://www.mamarobertos.com', 'http://www.subaruofmaple.com/', '1592167950', 'http://www.aaronvargaphotography.com', 'http://modernvascular.com/modern-vascular-of-glendale/', None, '1592167966', 'http://www.yourserenity.ca', 'http://fiveguys.ca', 'http://www.eddiebauer.com', 'http://cosmonailsmesa.com', 'http://www.christieclinic.com', None, 'http://vacationownershipconsultants.com', 'http://www.mcdonalds.com', 'http://www.wardenandsons.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.affirmhartman.com', 'http://rdnplumbing.net', 'http://www.allegromusicaz.com', 'http://www.bevsbeadz.com', 'http://www.phatpackshow.com/', None, 'http://www.bdcdental.ca', 'http://www.sweetnote.ca', 'https://4tenrealestate.com', 'https://www.painteddesertgc.com', 'http://www.marinoswickliffe.com/', 'http://www.delimarkcafes.com/477mtpleasant.html', None, 'https://www.r2smile.com', 'http://www.yelp.com/events/charlotte-hops-and-shops-2', '1592168035', 'http://www.rentcoldair.com/', None, 'http://7keystohealthinc.com/contact-us/', None, 'http://www.massageaddict.ca/mississaugameadowvale', 'http://www.stripper101.com/', None, None, 'http://www.quiktrip.com', 'http://pageperpage.com', 'http://www.stephencooley.com', '1592168063', 'http://www.torontopubliclibrary.ca/detail.jsp?R=LIB060&Entt=RDMLIB060', 'http://tradition.market', 'http://www.thepeacepipe.net', 'http://www.lasvegassuites.com/', None, None, None, '1592168082', 'https://locations.theupsstore.com/pa/pittsburgh/4885-mc-knight-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.hoopershealth.com', 'https://arizona.weidner.com/apartments/az/phoenix/roosevelt-row/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'http://www.centuryelectricllc.com', None, 'http://www.vieweyecare.com/', None, None, None, 'http://www.carusogourmetpizza.com/', 'https://locations.wendys.com/united-states/az/goodyear/1178-n-litchfield-rd', None, None, 'http://www.massimodutti.com/ca', 'http://www.restaurantrouge.com/', 'http://www.thesportspub.com/', 'http://www.ektaxandaccounting.com', 'https://locations.vitaminshoppe.com/az/scottsdale/vitamins-supplements-scottsdale-az-571.html', 'http://www.AgaveTreeAndLandscape.com', 'https://www.marks.com/en/stores/rexdale-etobicoke-55-woodbine-downs-blvd.html', None, 'https://www.thearrogantbutcher.com', 'http://www.adenearthworks.com', None, None, None, None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89084/600-in-north-las-vegas/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-600&utm_content=website-link&howheard=IYE', 'http://www.roserunkennel.com', 'https://www.thebso.com/locations/on/aurora/beauty-supply-outlet-haircuts-11847.html', 'http://www.allfireduplv.com', 'http://www.visitingangels.com/AZ', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3075+West+Liberty+Avenue-Dormont-PA-15216/storeid=4144?cid=ps_ylp_2020', 'http://www.conns.com/store-locator/north-carolina/charlotte-28273', None, None, None, None, 'http://www.superstarcarwashaz.com/w_services2.php', 'http://www.goldstockjewelers.com', None, 'https://www.uhaul.com/Locations/Self-Storage-near-Litchfield-Park-AZ-85340/721037/', 'https://locations.theupsstore.com/nv/henderson/631-n-stephanie-st?utm_source=Yext&utm_medium=organic&utm_campaign=Listings', None, 'http://eastvalleypulmonary.com', 'https://www.gucci.com/us/en/store/7014-east-camelback-road?utm_source=yelp_us&utm_medium=storemarketing&utm_campaign=retail_storepages_marcomm&utm_content=23016_bookapp', None, 'https://www.ritasice.com', None, 'http://www.joinrmxprofessionals.com', None, None, 'http://bartlegibson.com', 'http://www.progressivehome.com', 'http://www.elpolloloco.com/locations/store/3855', 'http://www.problindrepair.com', 'http://stacyneal.wvmbmesa.com', 'http://www.hyattcarcompany.com/', None, 'http://www.thebeehivegifts.com/', None, None, 'http://luckyboyburgershopphoenix.bestcafes.online', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Chandler-AZ-85226/922030/', '1592168214', 'http://jwmechanical.com', 'http://www.dogdaystempe.com', None, 'http://www.venetian.com', 'http://villageclubs.com', None, None, 'https://www.titlemax.com/store/phoenix-e-warner-az-41-title-loans/?utm_source=yelp&utm_medium=listing&utm_campaign=places&tmx_id=771c0159ac754cf&sf_traffic=paid_listing_yelp', 'https://risasdental.com/find-a-location/tempe/?utm_campaign=LocationPage&utm_medium=TempeYelpWebsite&utm_source=Yelp', 'https://www.robinsplumbing.com', None, 'http://www.kierlandcigars.doodlekit.com/', 'http://www.rtthomegroup.com', None, 'http://www.samifruits.com', None, 'http://www.zeppes.com', 'http://www.southshoresah.com', '1592168256', 'http://www.meetfreshcanada.com', 'http://www.chandlerfamilycare.com', 'http://www.dadanddaughterphotography.com', 'https://www.themattressmania.com', None, 'http://uberadventures.net', 'http://megatirecalgary.com', None, 'https://stayatthei.com', None, 'http://www.harborfreight.com', '1592168284', None, 'https://runpigrun.ca', None, 'http://pranamanana.com', 'http://www.isscogenerator.com/main/', None, 'http://www.runplusfun.com', '1592168301', 'http://www.bowlology.com', 'https://www.ulta.com/stores/henderson-nv-1191', 'http://chase.com', '1592168311', 'http://www.floorsforless.com', None, 'http://www.3030dundaswest.com', 'http://www.krankensigns.com/', 'http://www.laurellake.com', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', 'http://www.graceaz.com', 'https://www.roostersmgc.com/locations/nc/huntersville/torrence-village-haircuts-13194.html', 'http://www.greatclips.com/', 'http://omegamassage.ca/', None, 'http://www.wiler.org', None, 'http://azrattlers.com/', 'http://hawksgym.com', None, None, None, '1592168350', 'http://xaviermortimer.com', 'http://www.teejaysbrampton.com', 'http://leesliquorlv.com/locations/the-crane-bar', 'http://portofinocrs.com', 'http://www.mississauga.ca/', 'https://www.foresthillortho.com', None, 'http://my.clevelandclinic.org/departments/eye', '1592168367', 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', None, 'http://www.bk.com', 'http://www.urbanhomeandgarden.com', 'http://N8tiveArts.com', 'https://www.publicstorage.com/south-carolina/self-storage-lake-wylie-sc/29710-self-storage/2566?pid=wyelp&CID=1245&CHID=AFL', 'http://www.valleyairworks.com', None, 'https://www.vagaro.com/nailsbyyulie', 'http://www.schaffers.com/', None, 'https://www.eaglerider.com/phoenix', None, 'https://www.SearsHomeServices.com/locations/appliance-repair/nv-henderson/1245-w-warm-springs-rd', 'https://www.wellsfargo.com', 'http://www.makeupbykyra.com', 'http://encorecatering.com/', 'http://www.cbdemporiumaz.com', '1592168410', 'http://pawntnt.com', 'http://baywoodclinic.com', None, None, 'http://www.corvobartoronto.com', 'http://www.spicersprinklerworks.com/', None, 'http://www.expertnailandspa.com', 'http://cleaningservicecharlotte.net', None, 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', None, None, None, 'https://www.pods.com/locations/united-states/nevada/las-vegas', 'http://www.blackmountainortho.com', 'https://advancedvisioninstitute.net', 'http://christophersfinedrycleaning.ca', None, 'http://www.canvasgallery.ca', 'http://browart23rosspark.com', None, 'https://local.safeway.com/safeway/az/phoenix/810-e-glendale-ave.html', 'http://www.epiclandscapelv.com', 'http://local.buckle.com/nv/las-vegas/457/', 'http://italianoasispizzeria.com', 'http://www.lmca.org/about/lmcafe.cfm', None, 'http://www.flutedmushroom.com', None, 'http://cleaningwonders.com', 'https://www.msisurfaces.com/phoenix-countertop-showroom-distribution/?utm_source=yelp&utm_medium=cpc&utm_campaign=yelp_monthly', 'http://www.memphisstationbar.com/', 'http://www.berdenas.com', 'http://www.tacobell.com', None, None, 'http://www.jacobsonbrosdeli.com/', 'http://www.dornellas.com/', None, 'http://www.bikebike.ca', None, 'http://www.beautybrowsalon.com', 'http://www.theupsstore.ca/60', 'http://www.azmistsystems.com', 'http://www.ajsspamillennium.com/', None, 'http://www.dsw.com', 'http://www.elitefamilydental.com', None, 'http://solita.ca', None, 'http://www.hugoboss.com', 'https://horsebacktrailriding.com', None, 'http://www.cpk.com/location/details/Chandler', None, 'http://www.salonlevel6.com', 'http://www.twainandswensonstorage.com', None, None, None, None, 'http://www.fanniemay.com/', 'http://tavernedelaferme.ca', None, None, 'http://www.essentialskinaz.com', 'http://www.newcreationssalon.com', 'https://www.nevadalegalforms.com', 'http://www.masterhardwarepa.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.theinnersleeve.com', '1592168571', 'http://www.serviceking.com/locations/service-king-falconis?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'https://cinemark.com/nevada/century-16-santa-fe-station-and-xd', 'http://www.metrogreenscape.com', 'http://mkautomotive.com', 'http://www.teuschertoronto.com', None, None, None, None, 'http://www.dininginaz.com', 'http://sc-clinic.com/clinic/spadina-and-bloor/', None, None, 'http://www.maxumconstruction.net', 'https://www.walmart.com/store/6586/concord-nc/whats-new', 'http://www.smartpointresearch.com', 'https://www.cfshops.com/toronto-eaton-centre.html', 'http://www.elmnt.ca', 'http://dubaijewellers.ca', 'http://www.pizzabreak.ca/', 'http://labahiaasadosymariscoslasvegas.cafesonly.online', None, None, None, None, '1592168629', 'http://www.precisiontune.com/ConcordNC', 'http://beyerapplianceservice.com', 'http://www.completemarine.com', 'https://www.food4less.com/', None, None, None, 'http://sundevilpool.com', '1592168649', 'https://www.handandstoneballantyne.com', 'https://blackbeardiner.com/location/glendale/', 'http://fastlanepizza.com', 'http://www.arizonasrealty.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, None, None, 'http://k9-games.com', None, 'http://www.carolinashealthcare.org/charlotte-medical-clinic', 'http://www.gmurrayphoto.com', 'http://stcharlesonline.org', 'http://www.classiccakesaz.com', 'http://www.tiptopautocollision.com', None, 'http://www.fresh-burger.com/', 'http://www.lakesidesportschiro.com', 'http://flobarlounge.com', None, None, 'http://www.fat-tuesday.com', 'http://www.stowintegrityauto.com', 'http://experiencetheblackout.com/', 'http://www.charlotteappliancerepairmen.com', None, '1592168709', 'http://www.redtailgolfclub.com', 'https://www.balancinghormonesnaturally.com', 'http://www.emb-plus.com', 'http://famouslaffa.com/', 'http://stores.sportsauthority.com/az/phoenix/sporting-goods-phoenix-692.html', 'https://cigarsdaily.com', 'http://www.centralphoenixanimalhospital.com', 'https://lvfamilyvision.com', None, 'http://www.cuttingedgecalgary.com', 'http://www.rentaffordable.com', 'http://www.sunnydayslearningcenter.com', 'http://www.oasisspringsbuilders.com', 'http://www.surf-ski.com/', 'http://www.kwakballet.com', 'http://www.setmefree.ca', 'http://cashcanada.com/pawn-shop-location/cash-canada-forest-lawn', 'http://universalenroll.dhs.gov', 'http://www.kfc.com', None, 'http://www.haircutie.com', 'http://www.mcdonalds.com', 'http://frugalmuse.com', None, 'https://www.snaderlawgroup.com', 'http://www.acehardware.com/store-details/15917', None, 'http://www.stlouiswings.com', 'https://www.abuelos.com/restaurants/chandler/', None, 'http://www.shenanigansbarandgrille.com', None, 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'https://www.anytimefitness.com/gyms/3912/Litchfield-Park-AZ-85340/?utm_source=yelp&utm_medium=local', None, 'http://wynnfitness.com/location/mississauga', None, 'http://newvisionpropertymanagement.com/', 'http://www.islanddentalcenter.com', 'http://www.hootersarizona.com', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', None, 'https://lernerandrowe.com/?utm_source=Yelp', None, 'http://www.murrayhillfoods.com', '1592168804', None, 'https://locations.panerabread.com/il/aurora/1304-fox-valley-center.html', 'http://Therapeuticretreat.Com/', 'http://www.instantbeautyspa.com', None, 'http://www.nest.to/', 'http://alexblackgolf.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.verizonwireless.com/stores/ohio/streetsboro/streetsboro-357953/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.dollarama.com', 'http://www.gustafsonlawoffice.com', 'https://www.core704.com', 'https://dealer.sprint.com/experts-choice', None, 'http://www.dragonscandy.com', None, 'http://www.suncitysummerlinflorist.com/?srccode=yelp_track', 'http://www.smoknpig.com/', 'http://www.rahrawrahpetfood.com', None, None, 'https://arizona.weidner.com/apartments/az/phoenix/trailside-at-hermosa-pointe-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'https://dentistryofthecarolinas.com/locations/monroe/', None, 'http://www.timothys.ca', 'https://www.nofrills.ca/store-locator/?utm_campaign=Loblaws&storeId=1384&utm_medium=LPM&utm_source=G', None, 'http://www.lu-az.com', 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', 'https://tahdesign.com', None, None, 'https://www.alphagraphics.com/centers/charlotte-north-carolina-us287.html', None, None, None, 'http://www.sabas.com', None, None, 'http://www.picknsave.com', 'http://locations.harristeeter.com/nc/harrisburg/92/', '1592168889', 'http://all-tranz.com', None, 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', 'http://thefrogandcrown.com', 'http://popeyeschicken.ca/', 'http://www.muchoburrito.com', 'http://www.starbucks.com/store/17296/', 'http://www.stratospherehotel.com/american_superstars.html', 'http://www.foodlion.com', None, 'https://www.walmart.com/store/3473/las-vegas-nv/whats-new', 'http://www.hayashihibachi.com', 'http://www.aboutfaceaz.com', None, 'http://www.pizzanova.com', 'http://www.westowntire.com', '1592168925', 'https://www.potterybarn.com', 'http://www.burritoboyz.ca', 'http://www.oldnavy.com', 'https://firstcu.net', None, None, '1592168939', 'http://www.dontortaco.com', None, 'http://astoriacafemarket.com', 'http://downtownbrewfestival.com', None, 'http://www.papajohns.com', 'https://el-pollito-charro.business.site', None, 'http://www.asiaaz.com', 'https://www.currys.com', 'http://www.discount-drugmart.com', None, None, 'https://www.alamo.com/', 'https://www.coffeeatrio.com', 'https://www.studioemphotography.com/photographer-fairmont-scottsdale-princess', None, None, 'http://www.louiesnoodle.com', None, None, 'http://desertcovenursingcenter.com', 'http://parkviewmanor.ca', None, 'https://www.lumberliquidators.com/ll/stores/az/phoenix/2120-s-7th-street?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1019', None, None, 'http://www.chinapearl1.com/home', 'http://amoving.company', None, 'http://www.macgyverautobody.ca', None, 'https://local.fedex.com/oh/north-olmsted/office-1234/', None, 'http://www.poochesnpalsinc.com', 'http://www.hmsmokeshop.com', 'http://www.bankofamerica.com', 'http://www.a2bmovers.com', 'https://www.casareynapgh.com', None, 'http://www.smilecreationsaz.com', 'https://curaleaf.com/stores/nj', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.rounduplakecampground.com/', 'https://www.sunlifemaids.com', 'https://www.chevronwithtechron.com', 'http://sugarshacksweets.net/', None, 'http://www.stuffingtonbear.com/', None, 'http://www.myflightsurgeon.com', None, 'http://www.stavrossportsbar.com', 'http://www.teffngreens.ca', 'http://www.modern.yoga', 'http://www.fillsgas.com', '1592169057', 'https://local.fedex.com/pa/pittsburgh/office-2064/', 'http://www.scoopnyc.com', 'http://ourjourneytraining.com', None, 'https://www.camelbackautoglass.com', 'http://www.tempespeedandperformance.com', None, 'http://www.spartantrainingchandler.com/', 'http://www.tbirdmed.com', None, None, 'https://www.petsuppliesplus.com/Store/OH/Elyria/Elyria/123?utm_source=Yelp&utm_medium=Store-Page%C3%8A', 'http://www.enzositalianmarket.com', 'http://www.drlonlawrenz.com', 'https://www.anylabtestnow.com/franchises/las-vegas-89146/', 'https://stores.jcrew.com/en/south-hills-village', 'http://coachzinger.com', 'http://www.footsensation.ca/', 'http://www.assistbooks.com', None, 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', 'http://www.mcdonalds.com', 'http://www.adore2.com', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://transcanadacarrental.com', 'http://www.berryvinegifts.com', 'http://www.thewellnesscenter.org', 'http://www.lux-spa.com', 'http://www.shopkawaii.com/', '1592169123', 'http://www.playitagainsportsmadison.com', None, 'http://www.audichandler.com/index.htm', None, 'https://www.peets.com', None, None, 'http://www.hollandresidential.com/talise', None, 'http://www.insurrectionaleworks.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.domesticblissdesign.com', 'http://taniahairbraiding.com/', None, 'http://www.graceinlasvegas.com', 'http://www.damcomputermedic.com', 'http://lokacupunctureclinic.com', None, 'http://www.artistsplay.com/hub-cafe', None, None, 'http://www.thrifty.com/?campid=DS:YL_THR_20150109_HP', None, 'https://www.wingstop.com/location/wingstop-421-phoenix-az-85015/menu', None, 'http://clickserve.dartsearch.net/link/click?lid=43700006430792986&ds_s_kwgid=58700000444978510&ds_url_v=2', 'http://cogburnsbar.com', None, 'http://www.kidscoop.org/', 'http://sangrock.com', 'http://www.expertconcretecoatingsinc.com', None, 'http://www.braizenfoodtruck.com/wp1/', 'http://www.drraykim.com/', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.cjsitalianice.com', None, 'http://www.awinadvancedautobody.ca', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Calgary-AB-T2H1L6/840051/', 'http://www.doddslaw.com', 'http://www.stacyspitstopbbq.com', 'http://www.hbotofaz.org', 'http://www.flowershoppetempe.com', 'http://www.moderationsuit.com', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.montzauto.com/', None, '1592169237', 'http://www.foodkingmenu.com', None, 'https://cortland.com/apartments/cortland-whitehall/', None, 'http://tiffanynailshairscottsdale.com/', 'http://www.chocolatsfavoris.com', 'http://www.yogadigs.com/', None, 'http://www.estheticaglenmore.com/index.php', 'http://www.richmondhilltoyota.com/', None, 'http://www.advant-edgecurbing.com', 'http://www.juicestandard.com', None, 'http://nlasvegasvets.com', 'https://footsolutions.com/peoria/', None, 'http://www.themanorspa.ca/', 'http://www.intownsuites.com/locations/charlotte-northeast-chn/', None, None, None, '1592169289', 'http://www.allearzsavannahs.com/', 'http://www.CoronadoHeights.com', 'http://www.aimeecaballero.com', 'http://www.pinklotusmenu.com', 'http://www.myscrubsandmore.com', 'http://www.parmatireservice.net', None, 'http://myvillaroma.com/', 'https://boulderoaksca.com', 'http://www.livingstoninnmadison.com', '1592169315', 'http://www.duffsfamouswings.ca', 'https://www.sourceforsports.ca/en-CA/Stores/3-Adrenalin-Calgary-Source-For-Sports.aspx', None, 'https://budgetbicyclectr.com/used-bicycle-showroom-museum', 'http://arizonagoldendoodles.com', 'http://www.einsteinbros.com', None, 'http://chickenfootestatesales.com', 'http://www.joyli.net', 'http://stuartdayguitars.com', 'http://www.foodlion.com', 'http://www.mellowbentertainment.com', 'http://avenueb-pgh.com', 'http://www.superelectric.tv/pinball', 'http://www.backonthebar.com', 'http://www.dickssportinggoods.com/', None, None, None, 'https://www.6ixcycle.com/contact-us/', '1592169360', 'http://azcountertop.com', 'http://www.turnberrytowers.com', 'http://www.liftedtrucks.com', 'http://elwoodmotorsportsandcollision.com', 'https://www.wellsfargo.com', 'https://www.pier1.com/on/demandware.store/Sites-pier1_us-Site/default/LocalStore?storeId=1243', None, 'http://www.tntmobiledetail.com', 'http://mariscoensenada.com', 'http://www.rachelsyoungatart.com', None, 'http://www.outback.com/locations/az/gilbert', None, 'http://redmodernfurniture.com', 'http://www.savorcafecharlotte.com', 'https://www.finessecateringandevents.com', 'https://www.petpeoplestores.com/rocky-river-store.html', 'https://www.gregbryandds.com', 'https://www.searsclean.com/pittsburgh-pa', None, 'http://www.cobsbread.com/home/', 'http://www.mcnallyauto.com', None, '1592169413', 'https://palmbeachtan.com/locations/NC/Indian-Trail-Old-Monroe-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=AUG', 'http://www.monroevilleconventioncenter.com', 'http://www.moes.com', None, 'https://www.umcsn.com', 'https://www.chuckecheese.com/?utm_source=yelp.com&utm_medium=referral&utm_campaign=Branded_Profile_CTA&utm_content=Branded_Profile_CTA_399', 'http://www.markhambowl.com', 'http://www.maidpro.com/henderson-nv', 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=119&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-119', 'http://www.hairrehabaz.com', 'https://abraauto.com/abra-auto-location/1051-charlotte-nc-albemarle-road', None, 'http://www.gingerflowerstudio.com/', 'http://domenicspub.com/', 'http://www.angelpark.com/-ninos-kitchen', 'http://www.redonionlounge.com', None, 'https://introboutique.com', 'https://www.faema.ca', 'http://johnnyvegasgrill.com/', 'http://www.bakingatitsbest.com', None, 'http://www.phoenixpubliclibrary.org/Locations/Pages/Ocotillo.aspx', None, 'http://www.thedistrictatscottsdale.com', 'https://www.marriott.com/spas/lasjw-jw-marriott-las-vegas-resort-and-spa/spa-aquae/5013971/home-page.mi', None, None, 'http://www.chopstickfoods.com', 'http://www.denimanddiamondsmesaaz.com', 'http://www.azenergy.com/', None, 'http://motorlessmotionbicycles.com', None, 'http://Centurionmgmt.com', 'http://www.crossfitwestvalley.com', '1592169495', 'http://www.oldnavy.com', 'http://www.palaroos.com', '1592169503', 'https://www.libertytax.com/income-tax-preparation-locations/19248.html', 'http://www.timhortons.com', 'http://www.gusbrown.com', None, '1592169513', 'http://www.citypharmacylv.com', 'http://lm2investments.com', 'http://www.silverstatesoccerleague.org', None, None, 'http://www.xlntshutters.com', None, None, 'http://www.tomaydo.com/', None, None, 'https://www.gallusdetox.com', 'http://www.laveenalterations.com', None, 'https://www.redrobin.com', 'http://elcortezhotelcasino.com/', 'http://www.fasttracksolar.com/', 'http://www.maricopaac.com', 'http://www.pagesbooks.ca', 'http://www.shaneonealphotography.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://sites.google.com/publikfire.com/publikfire', None, 'http://www.patatemallette.com/fr', 'http://palmvalleyrehabilitation.com/?utm_source=yelp&utm_medium=organic', 'http://criticalaz.com', 'http://sweetfrogyogurt.com/locations/store/tarentum-pa', 'http://www.kmart.com/stores/nevada/las-vegas/3680.html', 'http://www.snugasabug.com/store', 'http://www.luplv.com', 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-bethany-home?utm_source=yelp&utm_medium=local&utm_campaign=Honorhealth_Medical_Group_Bethany_Home', 'http://www.greatclips.com', 'http://www.toysrus.com/family/index.jsp?camp=MISC:yelp:store:page:tru:111910&categoryId=2255956', '1592169583', None, 'http://www.cherrybombcoffee.ca', None, None, 'http://www.courtneyvista.com', 'http://lisasean.com', 'https://www3.hilton.com/en/hotels/nevada/elara-by-hilton-grand-vacations-center-strip-LASCSGV/index.html?SEO_id=YELP-GV-LASCSGV', 'https://shopused.com', 'http://swingshiftauto.com', 'http://nail-salons.dapeem.com/', None, None, 'http://www.lcbo.com', 'https://www.chick-fil-a.com/lee', 'http://www.starbucks.com/store/9298/', 'http://www.sidestogobbq.com/bbq-location/cleveland-hopkins-international-airport', 'http://www.itsjustlunch.com/', 'http://onestopnutrition.com', None, None, None, 'http://www.jamminjerkvegas.com', 'https://www.lifestorage.com/storage-units/north-carolina/charlotte/28270/109-near-matthews/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NC-109&utm_content=website-link&howheard=IYE', 'https://www.marriott.com/hotels/hotel-information/restaurant/yyzda-delta-hotels-toronto-airport-and-conference-centre', None, 'http://www.dragonpearl.ca', None, 'https://www.gianteagle.com/Stores/Store/?storeId=8%2F', None, None, None, None, 'http://www.adampinksalon.com', 'https://essencevegas.com/locations/las-vegas-strip/', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.blushlasvegas.com', 'http://www.autoglassfactoryaz.com', 'http://www.womensinternational.com', 'https://www.advancedmotionchiropractic.com', None, 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.blastedbarley.com', 'http://www.cvcclub.com', 'http://www.falafelcafecleveland.com', 'http://www.munails.com', 'https://www.gotenda.com', None, 'http://www.coffeerushcafe.com', 'http://www.azdeq.gov/EmissionsTest', 'http://www.RedesignUpholstery.com', None, 'http://www.olbrichbiergarten.com', 'http://doubletree3.hilton.com/en/hotels/ontario/doubletree-by-hilton-hotel-toronto-downtown-YTOCSDT/index.html?SEO_id=YELP-DT-YTOCSDT', 'http://www.northshorecommercialdoor.com', 'http://www.thewhiningpig.com', None, 'http://www.eastmeatswesthalal.com/', None, 'https://www.speedy.com/shops/toronto-danforth/en/', 'http://sandiegonailsphoenix.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.ingleside.com', 'https://soslawnmaintenance.com', None, None, 'http://www.deltamechanical.com', 'https://www.wyndhamhotels.com/hotel/02493?tel=18002521709&iata=00093785&cid=fe:ra:20161215:yl:pp:ramus:02493', '1592169733', 'https://www.speedway.com', 'http://www.gianteagle.com', 'http://www.theredzonemadison.com/', 'https://azcdps.com/locations/paradise-valley/', 'http://www.kitchenland-lv.com', 'http://www.squirrelhilloptometrist.com', 'https://stepuptowellnessnow.com', 'http://www.WestonTeamMortgageLoans.com', 'http://www.dreamlanes.com', '1592169756', None, 'http://www.eatfromatruck.com', None, 'http://www.coffeebytes.net', 'http://tahoepower.net/', None, 'http://www.cafedepariscanada.com', 'http://www.mecklenburgbridal.com', None, 'https://www.lasvegashomes.vegas', 'http://www.DrThompsonAZ.com', None, 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', 'https://www.ups.com/ca/en/help-center/contact.page', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.capstonerealtypros.com', 'https://ad.doubleclick.net/ddm/clk/459148250;262878939;b', None, None, None, 'https://www.clubpilates.com/tempe/', 'http://www.starbucks.com/', None, 'http://www.7-eleven.com/?yelp=29384', 'http://www.tribeamericaleathers.com', 'http://www.bravobridals.com', 'http://www.ipolished.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.vegasonerealty.com', 'https://procellmotorsports.com', None, 'http://www.subzimandi.ca', None, None, None, 'http://www.starbucks.com', 'http://theflatsatgranitereef.com', 'https://www.budsglassjoint.com', 'http://www.city-tavern.com', None, 'http://www.onceuponachildstow.com/', 'http://www.sonoranlifestyle.com/', 'http://auraspacalgary.com/', 'http://tfwestrella.com', 'http://www.lasvegaspaininstitutes.com', 'https://locations.monro.com/oh/fairlawn/111-ghent-road?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', None, 'http://www.doctorsofhair.com/', None, '1592169853', 'https://www.purebarre.com/location/central-phoenix-az', 'http://goodnbr.com', 'http://www.warholdmechanicals.com/', None, 'http://gmhairdesigncolorspecialist.com', 'http://www.michaeljohnsoncpa.com', 'http://robertsidell.com', 'http://www.lakeeriecrushers.com', None, 'https://www.wellsfargo.com', None, 'https://local.fedex.com/nc/charlotte/office-0746/', 'http://www.mrsub.ca', '1592169882', None, None, 'http://www.tempetrophy.com', 'http://www.pvlaserlipo.com/', 'https://www.quicknclean.net', 'https://www.signaturestyle.com/locations/on/toronto/first-choice-haircutters-5677.html', 'http://www.proficientclean.com', 'http://www.einsteinbros.com', 'https://www.kurevapes.com', None, 'https://unlvmedicine.org/family-medicine', 'http://www.7-eleven.com/?yelp=32265', None, 'https://theeggworks.com', 'http://www.aamcophoenixcentral.com', 'http://www.somacafe.com', 'http://www.ronherman.com', 'http://www.culligantotalwater.com', 'http://www.theweaveshop.com/north-carolina-charlotte/', 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'http://www.starbucks.ca', 'https://www.bluevaportech.com/', 'http://www.missbrow.com/', 'http://gqcutslasvegas.com', 'http://lasvegas.carenow.com/location/ann-simmons', 'http://allure4me.com', None, None, None, 'http://snvscooters.com', 'http://www.bownessauto.com', None, 'http://cowbridgefurniture.com', 'https://www.staples.com', 'http://www.youngbeautifulsalonspa.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://grilladestorino.com/fr/grillades-torino-place-vertu/', 'https://candy-cravers-coffee.business.site', 'https://www.xpo.com', 'https://www.supercuts.com/locations/oh/lakewood/lakewood-city-center-haircuts-83162.html', 'http://www.carters.com', 'https://arrowheadcoin.com', None, 'http://bytecle.com', 'http://www.bombayschutney.com', 'http://www.bookparkngo.com/index.php?main_page=charlotte', None, 'http://www.familydollar.com', 'http://thedetroiterlakewood.com', 'http://www.crownandanchorlv.com/', 'http://www.papajohns.com/', 'http://www.keffervw.com', 'https://www.choicehotels.com/arizona/scottsdale/comfort-suites-hotels/az816/rates', 'http://www.nardisfinedining.com', 'http://balilaffa.com', 'http://www.cabarruseye.com', 'https://stores.advanceautoparts.com/az/scottsdale/15475-northsight-blvd?utm_content=listing-2017-12-21&utm_medium=local&utm_source=yext&utm_campaign=aap', 'http://www.studiojewelerswi.com', 'http://www.mootowncreamery.com', None, 'https://locations.vitaminshoppe.com/oh/strongsville/vitamins-supplements-strongsville-oh-854.html', 'https://6ixtips.ca', 'http://www.pickeringhonda.com/', 'http://www.ericwelchpainting.com', 'http://www.harborfreight.com', None, 'http://www.childsplayaz.org', 'https://www.beallsplumbing.com', 'http://www.tatesac.com', None, None, 'http://www.roiimprovementsllc.com/', None, None, 'https://nevadaoralandfacialsurgery.com', 'https://www.barrhouseonmain.com', 'http://www.bankandbaronpub.com/', '1592170054', 'http://bluediamondlv.com', None, 'http://www.jfdayspa.com', 'http://www.pizzanova.com', 'https://www.thegalleryapthomes.com', 'http://www.elyriafence.com', 'http://www.bakerykaffeehaus.com', 'http://www.drteddysim.com/about-dr-teddy-sim/', 'http://www.gopropoolservice.com/', 'http://www.redressnyc.com/', 'http://charmeck.org/mecklenburg/county/ParkandRec/Parks/ParksByRegion/NorthRegion/Pages/Jetton.aspx', 'http://www.kbhome.com/new-homes-phoenix', 'http://www.freshbonsainails.ca', None, '1592170086', 'https://www.ediblearrangements.com/stores/2875-W-Ray-Rd-Chandler-AZ-85224', None, None, None, None, 'https://www.prosourcewholesale.com/showrooms/oh-prosource-of-cleveland', 'http://www.merrymaids.com', 'https://www.purchasegreen.com/locations/henderson-nv/', None, 'http://the-toy-box.com', None, None, None, None, 'http://www.buckle.com/', 'http://www.nostalgic-furniture.com', '1592170122', None, 'http://www.maximes.ca', 'http://www.allanimalsrescue.com', 'http://www.streetsvilleflorist.com/?srccode=yelp_track', 'http://www.roadrunnerexpresscarwash.com', 'http://www.cafemia.com', None, None, None, None, 'http://Tshsalon.simdif.com', None, None, 'http://www.rossstores.com', None, 'http://www.dirtyfoodto.com', None, None, 'https://www.bellissimafashions.com', None, 'http://www.dollarama.com/', None, None, 'http://www.azdentalheights.com', 'https://www.discounttire.com/store/az/mesa/s/1294?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', 'http://clickserve.dartsearch.net/link/click?lid=43700006430627338&ds_s_kwgid=58700000443429188&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.urbancrawfishstation.com', 'http://www.foothillsrehab.com/', 'http://www.holidayinn.com/hotels/us/en/brampton/ybmca/hoteldetail', 'http://www.eatkickshaw.com/index.php', 'http://www.hannahscaramelapples.com', 'http://center-for-growth.com', 'http://www.lux.salon', None, 'http://robertostacoshop.com', 'http://wagnwash.com/locations/phoenix-az/', 'http://www.thepoolmagician.com', 'http://pierrefonds.carstar.ca', None, 'http://www.riosantafeapts.com/?campaign_code=yelp_Rio_Santa_Fe_AZ_85323', 'http://www.arrowheadmartialarts.com', 'https://www.houseofhandsome.com', None, 'http://kristapsons.com', 'http://www.oldcreditbrewing.com', 'http://www.applehillanimalhospital.com/', 'http://www.ortconline.com', 'http://www.dasgasthaus.ca/', 'http://www.campthunderbird.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.34182.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:34182', None, 'http://www.starbucks.com/store/9298/', None, None, None, 'http://www.cronometro.com', None, 'http://www.salonmichaels.com', 'http://www.burlingtoncoatfactory.com/store-details-Store-213--5959-West-Sahara-Avenue--Las-Vegas--NV--89146-3126.aspx?id=2d282a9a-6b10-4437-bb42-7194af655b83&from=89146', 'http://www.fracosandfroccs.com/', 'http://luchitashudson.com', None, None, 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', '1592170265', 'http://www.hm.com', None, 'http://cranberry.sagahibachi.com', 'http://www.tortoisesupply.com', 'http://www.dominos.com', 'http://www.anchorsuprescuegroup.org', 'http://www.lovemycolon.com', None, 'https://grayhawkgolf.com/dining/the-morning-joint', 'http://etherealnails.com', '1592170292', 'https://www.niudanoodles.com', 'http://www.southwestrainbow.com', None, 'http://ad.doubleclick.net/ddm/clk/283420830;110240480;l', 'http://www.foodtruckcaravan.com', 'http://www.portraitinnovations.com/location/143/OH/Mayfield%20Heights/44124/Mayfield-Town-Center', None, 'http://www.hudsonoverheaddoors.com', 'http://www.meltingpot.com/greenvalley', None, 'http://aguamentiaz.com', None, None, 'http://www.rue21.com', '1592170325', 'http://www.valleyvistapoolcare.com', 'http://www.spirale.net/', 'http://fuegobistro.com/fuegotaco/', 'http://www.liasian.com', 'http://DeconResponseteam.com', None, 'http://www.gurtnerdental.com', 'http://www.timhortons.com/', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', 'https://www.oakandfort.ca/', 'http://jcls.jazzercise.com/facility/fountain-hills-jazzercise-center-14600', None, 'https://www.marriott.com/hotels/hotel-information/restaurant/cltad-ac-hotel-charlotte-city-center/', 'http://www.dvmcvet.vetsuite.com', None, 'http://plumbingsource.net', 'http://www.middleburgheights.com/?q=rentals_community_center', 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', None, 'http://www.sparkletime.net', None, 'http://www.playitagainsports.com', 'http://www.hrcleveland.com/tparrot.php', 'http://www.desertstorage.com/las-vegas-nv-boat-rv-storage', '1592170380', 'http://www.nakedcitylv.com', None, 'http://www.bathandbodyworks.com', None, 'http://www.hoipolloicafe.com', None, 'https://druxys.com/location/2-st-clair-ave-colonia-place/', 'http://www.plazahotelcasino.com', None, None, 'http://www.thespiritbox.com', 'https://www.patagoniaelements.ca/store/content/10/Calgary/', '1592170409', None, None, 'http://www.countrytireautomotive.ca', 'https://www.royaldistributing.com', 'https://www.presidentialpools.com/gilbert-swimming-pool-builder', 'http://www.gingersdesserts.com', None, None, None, 'http://www.vegasairductcleaning.com', None, 'http://www.betterlifemobility.com', 'http://www.azoral.com/', 'https://www.bellacinosofstow.com', '1592170442', 'https://totalimageoakville.biz', 'http://www.dayonepizzadelivery.com/', None, None, 'http://desotocentralmarket.com', None, 'http://www.eyedoctorchandleraz.com', None, 'http://eosfitness.com/location/pecos?utm_campaign=vegas-pecos&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', None, '1592170464', None, None, 'https://stores.jcpenney.com/pa/pittsburgh/clothing-stores-pittsburgh-pa-2263.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2263', None, None, 'http://www.thepamperedpinkie.com/', '1592170483', None, None, 'http://www.flightcentre.ca/', 'http://www.marshallsonline.com', '1592170491', 'https://www.gilbertaz.gov/departments/parks-and-recreation/parks-facility-rentals/parks-info-ramada-rentals/parks/crossroads-park', 'http://www.pair.com', '1592170499', 'https://organicnaillounge.business.site', None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.mathnasium.com/northwestlasvegas', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.eddietaxplus.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=3317&localechange=1', 'http://www.heroburgers.com', 'https://www1.shoppersdrugmart.ca', 'http://www.sackstierney.com', 'http://www.beastmodeonline.com', 'https://www.waxmans-carpet.com', 'http://myazinjury.com', 'http://www.mrappliance.com/east-valley', None, 'https://www.aritzia.com/en/store?StoreID=aritzia-bloor-flagship-toronto', 'http://www.northcalgarypediatricdentistry.com', 'https://skylineliquorstores.com', None, None, 'https://womensfitnessclubs.com/ajax/?utm_source=yelp&utm_medium=search&utm_campaign=yelpcampaign', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.siennalv.com', 'http://www.tomohibachiandsushi.com/', 'http://www.marriott.com/phxrn', None, None, 'http://www.avis.ca/', None, 'http://www.barriquesmarket.com', 'http://www.spirithalloween.com/', None, 'http://www.bigbenbarber.com', 'http://www.andoaz.com', 'http://www.klassykidsacademylv.com/', 'http://www.freddysusa.com', 'http://repweddings.com', None, None, 'https://www.voguerecoverycenter.com', '1592170593', None, None, 'https://www.planetfitness.com/gyms/streetsboro-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', None, 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=13080', None, 'https://hawkesclinic.com', None, 'https://www.johnnyscleveland.com', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Sun%20Prairie/WI/3289', 'http://libertyshawarma.com', None, 'http://www.altatempe.com', None, 'https://angel-dentalcare.com', 'http://www.pvcglendale.com', 'http://www.letspartyconsultants.com', 'https://www.wyndhamhotels.com/hotel/53380?tel=18003876085&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:53380', None, 'http://www.v-dubfurniture.com', 'http://www.sovpreschool.org', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.physio-logic.com', None, 'http://www.buca.ca/king.html', 'https://www.100thbgrestaurant.com', 'http://www.arizonaeyes.net', '1592170657', None, 'http://www.dollarama.com/', None, 'http://www.foxspizzamtwashington.com', None, 'https://stores.jcpenney.com/nv/lasvegas/clothing-stores-lasvegas-nv-2848.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2848', None, None, None, 'http://www.GoodByeDebt.com', 'http://www.starbucks.ca', 'http://www.icecastlearena.com', 'http://www.bestmatt.com/', None, 'http://www.fix8fitnesscafe.com', None, 'http://proem.org', None, None, None, 'http://www.sojoblau.com/', None, 'http://www.canyonstateedu.com', 'http://www.weavebaratl.com', 'http://www.assemblychefshall.com', None, 'https://dealer.sprint.com/preferred-wireless/find-a-store/67331-bridgeville-pa-15017', None, 'https://www.hydroplumbinginc.com', 'http://www.johnwallickjewelers.com', 'http://www.roastednutfactory.ca', 'http://www.hottopic.com/', 'http://www.azulorganicskincare.com', None, None, 'http://www.joyestes.net', 'http://www.jambajuice.com', None, 'http://www.traditionalelectric.ca', 'http://www.hatchyoga.com', None, 'http://www.harbsauto.com', 'http://www.TheKyotoBowl.com', 'http://www.sunnyviewdental.ca/georgetown', 'http://www.inkbombaz.com', 'http://locations.traderjoes.com/oh/woodmere/676/', 'https://www.starbucks.ca/store-locator/store/1017580/bayview-village-2901-bayview-avenue-toronto-on-m-2-k-1-e-9-ca', None, None, 'http://www.bulkbarn.ca/', None, None, 'https://www.supercuts.com/locations/az/surprise/albertsons-shopping-center-haircuts-82334.html', None, 'http://www.applewoodstorage.com', None, '1592170796', None, 'https://theprimerestaurantphx.wordpress.com', None, 'http://fitlifefusion.com', 'http://pazzoscatering.com', 'http://kaffirlimeindonesiancuisine.blogspot.ca', 'http://www.comicoasis.com', None, 'http://www.bigbztexasbbq.com', 'http://www.mrservice.ca', 'http://perennial-yoga.com', 'http://www.lovenspoonfuls.net', 'https://www.davidwmartinlaw.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.kireitoronto.com/', 'https://www.directcarpetone.com', 'http://www.bestratereferrals.com', None, '1592170850', 'http://www.dimpflmeierbakery.com', None, 'http://fabulashclt.com/', 'https://www.georgesflowers.net/?srccode=yelp_track', None, 'https://mintdentallasvegas.com', 'http://www.summerlink.com/wp-content/uploads/2010/03/2010ParkMap', None, 'http://www.southpittsburghvet.com', None, 'http://www.hpsc.ca', 'http://atlanticdentalphoenix.com/', 'http://www.middletonsports.com', 'http://www.californiathai.ca', 'http://www.albertaparks.ca/fish-creek.aspx', None, 'http://summitrestorationlv.com', 'http://serviceprowashandlube.com', 'http://bobcoffeebar.com', 'https://www.lhmfordmesa.com', 'http://www.dailyfreshgrillandcafe.com', 'http://www.houseofblues.com/lasvegas/crossroads', 'http://www.owensautorepair.com', None, None, None, 'http://www.halisangels.com', '1592170925', 'http://www.elixirspa.ca', 'http://www.phillyssportsgrill.com/', 'http://www.charlottecomedytheater.com/', 'http://www.dutildenim.com', 'http://www.treasureisland.com/restaurants/khotan.aspx', 'http://painstopclinics.com/pain-clinic-uptown/', None, 'https://www.modlash.net', None, None, 'http://www.cledogwalk.com', 'http://drivetime.com', '1592170963', 'http://www.bankofamerica.com', None, 'http://www.skyloft.com', 'http://nodayoga.com/', '1592170978', 'http://www.boosterjuice.com', 'http://www.letusrollyouone.com', None, 'https://www.anytimefitness.com/gyms/1069/Pineville-LA-71360/', 'https://iflycu.com', 'http://www.ysl.com/gb', 'http://www.southsidemotorspgh.com', 'https://www.ribeirojiujitsu.com/las-vegas-nevada.html', 'https://www.wellsfargo.com', None, 'https://medmen.com/stores/tempe-airport-phoenix-sky-harbor', None, None, 'http://www.allisonlovesfinejewelry.com', None, 'https://www.uhaul.com/Locations/Truck-rentals-near-Champaign-IL-61820/760043/', 'http://www.ojoslocos.com', 'http://beitshofarot.com', 'http://www.key.com', 'http://www.rainbowchiropracticcenter.com', 'http://www.rivenailandskincarespa.com', 'https://www.pancheros.com/locations/fitchburg', 'https://www.smilesquadlv.com', 'http://www.southfacese.com', 'https://www.bankofamerica.com', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=977', None, '1592171054', None, 'http://Rentmyrims.com', '1592172433', 'http://www.nevadaspca.org', None, 'http://extremecleantoday.ca/', None, 'http://www.runningroom.com', 'http://www.primarypetcare.com', 'http://www.extremeautocustoms.com', 'http://www.drivingforce.ca', 'http://www.clarkbrands.com', 'http://www.ilovemichaels.com/', 'https://hansenfamilyplumbing.com', 'https://www.ductz.com/north-phoenix-deer-valley/', 'http://www.klosekniturbana.com/', 'http://purebarre.com', None, 'http://renewedbeautyspecialists.com/', 'https://elevationchurch.org/locations/blakeney/', 'http://www.goodlifefitness.com/', 'https://www.selfstoragesolutions.com/self-storage/az/gilbert/85297/421?utm_source=yelp&utm_medium=cpc&utm_campaign=Gilbert', None, None, None, None, 'http://www.drainproplumbing.com', 'http://www.Charleys.com', 'http://www.mtsystems.ca/', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.olivegarden.com/locations/az/scottsdale/scottsdale-e-cactus-rd/1234?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:scottsdale-az-1234_pl:locurl_rd:1175', None, 'http://www.woofswigglesnwags.com', None, None, None, 'http://www.lasvegasnannies.com', 'http://www.sixthcitycycles.com', 'https://fancypetsaz.com', 'http://haymakersportsgrill.com', 'http://Elegantentrysarizona.com', 'http://www.avalonmeatcandy.com', None, 'http://www.theargusrealestatecompany.com', '1592172552', 'http://www.pizzasola.com/eastside.html', 'http://www.arizonabartenders.com', None, None, None, 'http://www.morningstarstorage.com/location/308/sc/fort-mill/carowinds/?ref=yelp', 'http://www.dynamitemontessori.com/', None, 'http://aandbroofing.net', 'https://www.kenganleynissan.com', 'http://www.janthonysalonspa.com/', 'http://rawlicious.ca/canada/locations/markham', '1592172590', 'http://www.illinistor-it.com', None, 'http://www.truevalue.com/mcfarlandtruevalue', None, None, None, None, 'https://www.brakesplus.com', 'https://www.scottsdaleaz.gov/parks/scottsdale-civic-center', 'http://www.athenaswindows.com', 'http://fishkinggrill.com', 'https://locations.davidstea.com/ab-calgary-111', 'http://www.salaradesserts.com', None, None, 'http://www.belle-image.ca/', None, None, 'http://bootlegsmokehouse.com', 'https://www.jasonsdeli.com/restaurants/maryland-pkwy-deli', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', '1592172650', 'http://gotorickys.com', 'http://www.morrowparkcityapts.com', 'http://epicentrenc.com', 'http://www.marketonmacleod.com', '1592172664', None, 'http://subsecreto.com', 'http://www.Barking-Dogs.com', 'http://www.punjabitadka.ca/', None, None, 'http://southeastcrabfeast.com/', 'https://www.tanrepublic.com/locations/nevada/las-vegas/maryland-parkway', 'http://www.mattressfirm.com/', 'http://www.greathousesportsgrill.com', 'http://www.thaihouse.us/', 'https://www.aircanada.com/us/en/aco/home.html', 'http://www.substationii.com', 'http://www.greatwallchinese-lasvegas.com', 'https://www.childhelp.org/advocacy-centers/childrens-center-of-arizona/', None, 'http://www.therefinerycc.com', 'http://onsitetinter.com', 'http://harvestcompassioncenter.org', None, None, None, 'http://www.ohstudiolv.com', 'https://sgplaw.com', 'http://www.failteirishpub.ca/', None, 'https://stores.loft.com/outlet/us/nv/las-vegas/7400-las-vegas-blvd-south.html', 'http://www.paradisebakery.com/', 'http://www.osigym.com', None, None, 'https://www.uniquenailbargateway101.com', 'https://www.quarryparkchiropractic.com', 'http://www.easternfootspa.ca', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://paintingwithatwist.com/avon/', 'http://www.urepmaids.com', 'http://www.entebella.com', None, None, 'https://www.springboardrecovery.com', None, 'http://www.pekingexpress.ca', None, None, 'http://www.red9ine.com', 'http://swift-moving.com', 'http://www.frontgate.com/Frontgate/US/CustomerService/Scottsdale/landing-path', 'http://www.greatexpressions.com/dental-offices/ohio-offices/severance', None, None, 'https://www.ulta.com/stores/macedonia-oh-1004', None, None, 'https://www.sitesmartmarketing.com', '1592172812', 'https://www.hilton.com/en/hotels/phxsrhx-hampton-suites-phoenix-surprise/?SEO_id=YELP-HP-PHXSRHX', 'http://patriciangrill.com/', 'http://www.1800waterdamage.com/phoenix-az', None, None, 'http://www.theelranchomotel.com', 'http://falbobrospizza.com', None, 'http://www.noahsnaturalfoods.ca', 'http://vitalshipmed.com', 'https://www.walgreens.com/locator/walgreens-4900+library+rd-bethel+park-pa-15102/id=11296', None, 'http://www.aboutadog.ca/', None, 'http://www.palacestation.com/entertainment/jacks/?utm_term=PS&utm_content=PS-PROPERTIES&utm_medium=SOCIAL&utm_source=YELP&utm_campaign=PS-YELP', None, 'http://www.telaverdeapts.net', 'http://www.skinpossible.ca', None, 'https://www.fordonfifth.com', None, None, 'http://www.gamestop.com', None, 'http://www.rentawrecktoronto.com', 'http://www.fitworks.com/rockyriver', 'http://www.calderawealth.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://extendedstayhotels.com', 'http://jc101services.com', 'http://www.palladinoscleaning.com/', 'https://www.haydenparkapartmenthomes.com', 'http://www.cyclepathnorthyork.com/', 'http://www.starbucks.com/store/69863/', None, None, 'https://www.visioncenterslv.com', None, 'http://makeupmagic.net', None, 'http://therapeuticmethod.net', '1592172922', 'http://www.tlc-airconditioning.com', None, 'https://urbanlivestockvet.com', None, 'https://www.nvisioncenters.com/locations/las-vegas/nevada-eye-care-east/?utm_source=directory&utm_medium=yelp', 'https://www.spectrumdermatology.com', 'https://www.intownsuites.com/extended-stay-locations/arizona/phoenix/west-2/', 'https://beautyenhancementsbyd.com', 'http://www.veneziabakery.ca', None, None, 'http://www.dentscharlotte.com', None, 'http://www.pethavenaz.com', None, 'http://exclusivelytankless.com', None, None, 'http://insurance-agency.amfam.com/AZ/tryna-hoerger-owens/default.aspx?sourceid=agp0001015578', 'http://laterna.ca/', None, 'http://affordableframingaz.com', None, 'http://blackcablimo.wix.com/blackcab', '1592172980', 'http://www.newfoodorder.com', 'http://lolasgelato.ca', 'http://www.tonibulloni.com/', None, None, None, 'http://www.rebath.com/location/lasvegas', 'http://www.acuhealings.com/', 'http://viapanini.ca', None, 'https://www.wyndhamhotels.com/hotel/14408?tel=18008899735&iata=00065402&cid=fe:hj:20170523:yl:pp:hjus:14408', None, None, 'http://ccsunscreens.com/', 'http://tazikiscafe.com/location/charlotte', '1592173013', 'http://www.effortlessmobileauto.com/servicesPhoenix/servicesPhoenix.html', 'http://fukuburger.squarespace.com', None, 'http://www.empowerpt.com', None, 'http://khalsamontessori.org/', 'http://www.mayfieldnissan.com/', 'http://quintealias.com', 'http://www.starbucks.com/store/9229/', None, 'http://www.fatburger.com/home/', 'http://cvdentalcare.com/contact-us-citrus-valley/', 'http://www.bonniesyarncrafts.com', 'http://www.nedrebos.com', 'http://www.ThePMFirm.com', None, 'https://www.xmsweetconnections.com', None, '1592173062', None, 'http://www.ivandianaphotography.com', 'http://www.dunkindonuts.com', '1592173071', 'http://www.cbac.com/sun-prairie?utm_source=Social&utm_medium=Yelp', 'http://www.threebrothersbarandgrill.com', None, 'http://www.cabinforlife.ca', None, 'https://www.azsolarconcepts.com', 'http://mwsvegas.com', 'http://scottsdalecosmeticdr.com', 'http://www.southsidejewelers.com', None, 'https://www.drtroell.com', 'https://www.coolrunningsautomotiverepair.com', 'http://www.stop-n-go.com', 'https://www.zimbrickchevrolet.com', 'http://www.preciouspets702.net', 'http://www.structube.com', 'http://www.middleroadbarbershop.com', 'https://karenshallmarkshops.com', 'http://www.midaslocator.com/AutoRepairFinder/tabid/151/Default.aspx', 'http://www.springdayspa.com', None, 'http://ridgeparkurgentcare.com', 'https://www.spectrumeyecarenc.com', 'http://vinoandpanino.com', 'http://orangeleafyogurt.com', 'http://weddingsbybonnie.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.richardmilleusa.com', 'http://www.chaneyscollision.com', 'http://www.townshoes.com/', 'http://www.indulgeyourselfsalon.com/', None, 'https://www.luxurypad.vegas', 'http://wanleeloy.com/', 'http://mindbrainlv.com', 'https://www.eatnpark.com', 'http://lerock403.com/', 'http://www.quiznos.com', 'http://www.crossfitculmination.com', None, None, 'http://www.shadowridgeapartmenthomes.com', None, 'http://le-cue.com/', 'http://www.carolinashealthcare.org', 'http://americanbrosplumbingco.com', 'http://www.thepalmsapts.com', None, 'http://www.bk.com', 'http://www.daracap.com', 'http://www.selectphysicaltherapy.com', 'https://www.premierworkspaces.com/nevada/henderson-augusta-park?utm_campaign=Yelp&utm_source=Yelp%20Organic', 'http://www.aulaz.com', 'https://locations.whataburger.com/az/goodyear/14251-west-indian-school-bypass.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', 'http://bullandfinchbars.com', 'http://www.harkinstheatres.com/theatreDetails.aspx?theatreId=4527', None, 'http://www.stfrancisdesaleslv.org', 'http://www.SallyBeauty.com', None, None, 'http://www.ljsilvers.com', None, '1592173210', 'www.brokenplate.ca', None, 'https://www.taylorstmgmt.com', None, 'http://www.swrandalltoys.com', 'http://www.factorydirect.ca', 'https://champsfamilyautomotive.com', 'http://www.orbitzcleaning.com', None, 'https://www.choicehotels.com/pennsylvania/pittsburgh/sleep-inn-hotels/pa744/rates', 'http://www.krispykreme.com', None, 'http://www.jacksonpt.com', None, None, None, None, 'http://www.6az.com/', 'http://www.ynhcclinic.com/', 'http://www.altafillmore.com', None, 'http://www.untitledandco.com', 'http://www.thesodashop.co', 'https://www.themarketphx.com', 'http://www.dqlunchforless.com', 'http://www.yourmovingsolutions.com/?utm_source=Yelp', 'http://miketheplumbercharlotte.com', 'http://www.lasvegasjeepandoffroad.com', 'http://www.oldnavy.com/products/las-vegas-nv-store-5811.jsp', 'http://www.starliquor.ca/', 'http://www.thefrenchbee.com', 'http://www.jeffsnotary.com/', None, None, 'http://pettis-pizza.com', None, 'http://www.rajdhanisweets.ca', 'http://www.simsgm.com/', None, 'https://joefilter.com', 'https://www.maaco.com/locations/az/glendale-11376/', 'http://www.pandaexpress.com/', 'http://www.meineke.com/', 'http://www.dunkindonuts.com', 'http://www.urbanhakka.ca', None, 'http://www.sweetrubyjane.com', None, None, None, 'http://www.legacybungalowsapts.com', 'http://www.getbooked.com', 'https://www.moes.com/find-a-moes/pennsylvania/murrysville/3428?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', 'http://www.mrpuffs.com/', 'http://www.dibeads.com', 'https://www.carstar.ca/en/locations/ab/calgary/carstar-calgary-sunridge-16118/', None, 'http://www.colormebella.com', 'https://www.wilhelmautomotivelitchfield.com', 'http://www.valleverdecarwash.com', None, 'http://www.lapetite.com/your-local-school/las-vegas-nv-7300/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'https://local.fedex.com/nc/gastonia/MRNA/?cmp=LOC-1001545-3-2-971-1110000-US-US-EN-YEXTLISTFEDEXSC', None, 'http://www.escapeloungelasvegas.com', 'http://azlifts4less.com', 'https://scottsdaleair.com', None, None, 'http://www.studiofivehair.com', None, 'http://www.insidethebungalow.com', 'http://www.health4lifenv.com', 'http://www.llbcpa.com/#dxEvq', 'http://www.fantasticsams.com', 'http://www.greatclips.com/', None, 'http://www.carolinafireplacerepair.com', None, 'http://www.dickies.com', None, 'http://www.cavabienspa.com/', None, None, None, 'http://beijingchinesecuisine.com', 'https://www.shoeshow.com', 'http://www.orangeleafyogurt.com', 'http://www.starbucks.com/store/8054/', None, None, None, 'http://www.sunshinemoon.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.stevesultimateair.com', 'https://www.wingstop.com/location/wingstop-1117-cleveland-oh-44128/menu', None, 'http://www.inspectslasvegas.com', None, None, None, 'http://www.barefoot-acupuncture.com/', 'http://www.kxyorkville.com/', 'http://flamebroilerusa.com', None, None, None, 'http://www.dragongemchinese.com/', 'https://www.collegecutiescleaningcars.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.fieldservicesaudio.com', 'http://www.lasvegastransportation.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.redrockcanyonlv.org', 'http://www.yongesheppardcentre.com', None, None, 'http://locations.jjill.com/az/scottsdale/65', 'http://www.savourfinefoods.com', 'http://www.twosphotobooth.com', 'https://ccv.church/locations/midtown-phoenix', '1592173504', None, None, None, 'http://www.pmcpropertygroup.com/', 'http://www.citywidemovers.ca/', 'http://www.apnursery.com', 'https://www.extraspace.com/storage/facilities/us/california/glendale/299955/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, 'http://www.sndk9.com/', 'https://local.pharmacy.safeway.com/az/scottsdale/7920-e-chaparral-rd.html', 'https://zoeskitchen.com/locations/store/az/mcdowell', '1592173529', None, 'http://kickinkitchenfoodtruck.com', None, 'http://www.lxvestudios.com', 'http://www.themugshottavern.com/', 'http://www.kravelasvegas.com/', None, 'http://www.noodlewok.com/', 'http://www.gigiscupcakesusa.com/ahwatukee-arizona', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.classictattoowilloughbyoh.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'http://www.davidduncanhouse.com', 'http://www.Totallymadeover.com', None, 'http://www.cccakesbybrandi.com', 'http://www.thankqrentals.net', '1592173562', None, None, None, None, 'http://www.grcogrill.com', 'http://www.cantinalaredo.com/location/scottsdale-arizona/', 'http://www.japaneats.ca', None, 'https://www.esso.ca/en/gas-station/vaughan-on-majormacvelloreesso-200302606', 'http://www.jordansrefurbishing.com', 'http://www.gyrostown.com', 'http://www.eddiebauer.com', None, 'http://www.serenityspalounge.com', 'http://www.timhortons.com', 'http://www.iphotoshop.com/', 'http://h5helicopters.com', 'https://www.fahadrestaurant.com', 'http://www.relocationservicescanada.ca', 'http://redcanyondentistry.com', 'http://www.quaker.org/pghpamm/', 'http://www.loveyourposture.com', 'http://www.manilabbq.com', 'http://www.kelseys.ca', None, 'http://www.baskinrobbins.com', 'https://www.boutiquewebsites.ca/website-designs.html', None, 'http://www.decatarina.com', 'http://www.felixswimschools.com/locations-schedules/woodbridge', 'http://www.magictouchmobiledetail.com', 'http://www.shenandoahmill.com', 'http://www.lovinghut.ca', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FLASHH', 'http://www.molonlabe.com', None, None, 'http://www.bundlebuilders.net', 'http://www.thebrewteabar.com', '1592173643', 'http://thecellarsalon.com', None, 'http://carambamex.com', 'http://villagepubcasino.com', None, 'http://www.cainpark.com', 'http://www.fairwaysapartmenthomes.com', 'https://www.athome.com/store-detail/?StoreID=North%20Carolina-Charlotte&utm_source=yelp&utm_medium=paidprofile', 'http://www.midas.com/toronto/store.aspx?shopnum=9827&dmanum=857001', None, 'https://www.bannerhealth.com/locations/phoenix/surgicenter', 'http://www.bestdealsauto.ca', 'http://www.dunkindonuts.com', None, 'http://dekra.us/en/nevada/henderson-26-w-horizon-ridge-pky/', 'http://www.pizzapizza.ca/', 'http://www.urbanfarm.org', 'http://fairgreenlawncare.com', 'http://www.flamingicecube.com', 'http://tnailslasvegas.com/', 'http://countrybarpeoria.com/', 'http://www.magicofjasonbird.com', 'http://kidsinclearningcenters.com/chandler-watermark/', 'http://www.jimenezarmsinc.com', 'https://www.squawpeakhilton.com/dining?_ga=2.50950569.1853949617.1562623293-1431667612.1561583712', 'http://www.madisontranquilitymassage.com', None, 'http://spgilbert.com', 'http://www.siamthaipgh.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.doraziolawgroup.com', 'http://www.highlandinnlasvegas.com', 'https://www.uhaul.com/Locations/Trailer-Hitches-near-Charlotte-NC-28217/780053/', 'https://www.walgreens.com/locator/walgreens-6906+university+blvd-moon+township-pa-15108/id=10917', 'http://www.rinxtoronto.com', 'http://kingskitchen.org/', 'http://www.wholehealth4life.org', None, 'http://www.velocityautobody.com', 'http://www.hotpinkteahouse.com', None, 'http://www.showtimetourslv.com/', 'https://www.dominos.com', None, '1592173746', 'https://us.petvalu.com/location/6058', 'http://illinois.edu', None, 'http://www.arizonaeliteproperties.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', '1592173758', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.missspice.ca', 'http://www.24-7electricalservices.com/', None, 'http://www.familydollar.com', 'http://bchcares.org', 'https://www.walgreens.com/locator/walgreens-2324+w+war+memorial+dr-peoria-il-61614/id=6408', None, 'http://www.unforgettablecoatings.com/', 'https://www.purebarre.com/location/fort-mill-sc', 'http://www.starbucks.com/store/9289/', '1592173785', 'http://someburros.com/', 'https://chatters.ca', 'http://salsaritas.com', 'http://www.barbiesgrill.com', None, 'http://www.cleyards.com', 'http://www.onenevada.org', 'http://www.spectrac.com', 'http://www.hortfrontiers.com', None, 'http://pursuitcf.com', None, None, 'http://www.qcreflex.com/', 'http://www.azwhiteningspa.com/index.html', 'http://www.houseofathens.com', 'http://www.firstclassprinting.ca/', None, 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'https://crissangel.com', 'http://TignorGroup.com', 'http://www.davismagic.com/', 'https://www.kellerhearing.com', 'http://www.cannabisclinics.ca/medical-marijuana-canada-clinic/#1440516223690-62dfe946-9e59', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreId=976', 'http://www.oasisbeautyspa.ca', 'http://www.sushiplus.ca/', '1592173848', '1592173850', 'http://www.searshometownstores.com/home/az/fountain-hills/1841', '1592173854', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', None, None, None, 'http://www.furnitureworld1.com', None, None, 'http://www.bellagioapts.com/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', None, None, None, 'https://cell-computers-and-games.business.site', '1592173881', 'https://mamajuliannes.com', 'https://backyourhero.com', 'http://www.theplacerestaurant.ca', 'http://www.urbanbulkandrefill.com', 'https://www.lumberliquidators.com/ll/stores/nc/matthews/11101-east-independence-blvd?utm_source=yelp&utm_medium=local&utm_campaign=yext&utm_content=1264', None, 'http://www.marengospa.com', 'http://dialabottle.ca', None, 'https://ad.doubleclick.net/ddm/clk/434342189;236814625;k', None, None, 'http://riotanlasvegas.com/wordpress1/', None, 'http://www.alyciamoore.com', 'http://abdappraise.com', 'http://www.fatbastardburrito.ca', 'http://abakeshop.com', 'http://www.mesabilliards.com', None, 'http://www.marbleslab.ca', 'https://townandcountrybarbershop.com', None, 'http://www.covenantday.org', 'http://www.lakenormanpaintandbody.com', None, None, 'http://www.elitemassagecalgary.ca', 'http://www.cccnevada.com/doctor/g-h-kashef-md/', None, 'https://www.huntington.com/Community/branch-info?locationId=23476', None, 'http://www.bivfaz.com', 'http://www.metro.ca', 'http://www.vegashot.com', 'http://www.crossroadsvet-painesville.com', 'http://www.baskinrobbins.com', None, 'http://www.XtremeExtensions.com', 'http://www.arbys.com', 'http://www.scottsdaleaz.gov/preserve.asp', None, '1592173969', None, 'http://vivaviolins.com/', 'http://www.fionnmaccools.com/locations/brampton-ray-lawson', 'https://www.wingstop.com/location/wingstop-421-phoenix-az-85015/menu', '1592173979', 'https://www.sprouts.com/stores/details/-/store-details/view/store/2/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'http://www.maidpro.com/phoenix-north', 'http://www.kingputtlv.com', 'http://mysuboxonedoctor.com', 'http://www.ivylasersalon.com', 'http://www.kofeinstitute.com', 'https://www.extraspace.com/storage/facilities/us/nevada/las_vegas/300031/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.laredosrestaurante.com', 'http://www.wizardofsuds.net', 'http://www.ontarioparks.com/park/voyageur', None, 'https://excelprimarycare.com', None, None, 'https://www.malakjewelers.com', 'http://www.clevelandishome.com', 'http://www.pattysheart.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.marrakechrestaurant.ca', 'http://the-yellow-penthouse.business.site', None, None, None, 'http://www.jjbrewco.com', 'http://www.piccoloantiquemall.com', 'http://www.divinethreading.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.allthingstea.ca', 'http://www-rivera-custom-painting.com/PROFILE', 'http://www.moxieinkdesigns.com', 'http://www.royaljade.ca', 'https://honorhealth.com/locations/primary-care/honorhealth-medical-group-east-tempe', 'https://www.napaonline.com', None, None, 'http://www.abpreschool.com/', 'http://www.ryanssalons.com', 'http://www.scottsdaleaz.gov/parks/cactuspool.asp', 'https://carolinacleanerscharlotte.com', 'http://www.goldsgymcalgary.ca', None, 'https://diceandbeansboardgamecafe.com', None, None, 'https://www.desertfinancial.com/Home/BranchDetails?branchId=1', 'http://www.trendautomotive.com', None, None, 'http://www.isaacjewelers.com', None, '1592174106', 'http://www.ashfordplaceapartments.com', 'https://store.vioc.com/nv/las-vegas/9631-trailwood-dr-89134-HC0003', '1592174114', '1592174118', None, None, None, 'http://pitapitusa.com', None, 'http://meridianlv.com/', None, 'https://www.casinoarizona.com/dining/eagles-buffet/', None, None, None, 'http://www.haggen.com', 'http://www.brickpointingpittsburgh.com', None, None, None, 'http://pennhills.org', 'http://rrrc.run', 'http://www.sunterramarket.com', 'http://www.pastorsautoservice.com', 'http://lvhottubs.com', 'http://l.macys.com/university-heights-oh?cm_mmc=Yelp_Stores-_-UniversityHeights-_-n-_-578&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=University+Heights_578&m_ac=yelp_stores&m_ag=n', None, 'http://www.mychickenshack.com', 'http://angelschristianacademy.com/landing.php', None, 'http://www.housing.wisc.edu/universityapartments/eheights', 'http://www.evaszabo.com', 'http://www.dentalemergencyservices.ca', None, None, None, '1592174202', 'https://container36.wixsite.com/wtrn', 'http://www.artisanhairstudio.net', 'http://www.desertheatwindowwash.com', 'http://www.thedoctorfence.com', None, None, '1592174224', None, 'https://www.choicehotels.com/north-carolina/charlotte/suburban-hotels/nc533/rates', 'http://www.goodmanslandscape.com/', None, None, None, '1592174241', 'http://www.getthelook.com/salondetail/default.asp?salonid=61146', 'http://www.adamsroadsidetowing.com/', None, None, None, 'http://www.aalltechmobile.com', 'http://www.hoopdome.com', None, 'http://www.nrsinjurylaw.com', None, 'http://www.coldwaterroofing.com', 'http://www.MassagesByChelsa.squarespace.com', 'https://www.wallacebethelparkflower.com', None, 'https://www.richerlifecounseling.com', 'https://someburros.com', None, 'http://marcelos-az-barbershop.business.site', None, None, 'http://cowtownbeefshack.ca', 'http://cooperscarpetandtilecleaningaz.com', 'http://alexbeauregard.com', None, None, '1592174306', None, None, None, 'http://www.wrapcitydesigns.com', None, 'http://www.southshoresah.com', 'http://www.balzacs.com/locations/distillery-district/', '1592174326', 'https://npidb.org/organizations/physician_assistants/family_363lf0000x/1386110443.aspx', None, None, None, None, None, None, 'https://www.americandiscountfoodsaz.com', 'http://www.JenniferKostuchowski.MyHomeHQ.biz', 'http://www.sweetdaddycupcakes.com/locations.html', None, None, 'http://www.drbarin.com', 'https://nuancelasvegas.com', '1592174369', None, 'https://www.petsmart.ca/stores/ca/on/scarborough-store2009.html?utm_campaign=us-lcl-srv-eg&utm_medium=listing&utm_source=yelp', 'https://goppa.org', None, None, 'https://www.perplexitygames.com', 'http://www.printystamp.com', 'https://alfredopatisserie.com', 'http://ipacupuncture.com/', None, 'https://hirosushi.to', 'http://www.verizonwireless.com/', 'https://www.peopleready.com/locations/las-vegas-nv-1144', 'http://hancockfabrics.com/', None, 'http://www.welltracnv.com', 'http://www.greenstarautocenter.com', 'http://www.pmkbar.com', None, None, None, None, 'http://www.bhhsnv.com', 'http://www.dhslv.com', None, 'http://www.airportparkingreservations.com/lot_ez_airport_parking_yyz', None, 'http://www.andysfishandchips.com', None, None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1212+South+Greenfield+Road-Mesa-AZ-85204/storeid=5026?cid=ps_ylp_2020', None, None, 'http://www.alwaysjumping.com', 'https://www.mimiscafe.com/locations/glendale/', 'https://www.streetsideclassics.com', 'https://healinghandshannah.com', 'http://www.wendys.com', 'https://nationwidevision.com/locations', 'http://www.canadiantire.ca/en/store-details/on/toronto-main-danforth-on.store.html', None, 'https://globalautoscarrentals.com', 'https://www.sonoraquest.com/find-a-location/phoenix-by-appointment-only-tatum-shea/', 'http://www.gnc.com/', 'https://www.residentculturebrewing.com', 'http://www.ucalgaryrecreation.ca', 'http://www.sheaparc.com', None, 'http://www.windowuniversecleveland.com', 'http://www.marvelousmousetravels.com', None, '1592174529', 'http://www.eraagelessfuture.com', 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', None, 'http://www.gap.com', '1592174544', 'http://www.floweramacleveland.com', 'http://www.mycdi.com/arizona/insight_imaging_-_arrowhead/', None, None, 'http://www.perfectblend.ca', 'https://locations.theupsstore.com/pa/moon-township/5990-university-blvd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.laseraway.com/locations/nv/las-vegas/?utm_source=yelp+organic&utm_medium=website+link', 'http://www.fabfred.com/locations/trailwood-drive/', None, 'http://www.srsengineshop.com', 'http://studiooftens.com', '1592174581', None, 'http://www.pcfarm.ca', None, 'https://www.cartelcoffeelab.com/pages/5th-avenue', 'http://www.disantopizza.com', None, 'http://www.heritagefishnchips.com', 'http://www.needle-pin.com', 'https://speeders.ca/calgary/', 'http://www.countryhillsmassage.com', 'http://www.fedmc.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360246&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://tempeautoshop.com', None, 'http://www.silverstatecu.com', 'https://www.monicals.com/locations/monicals-pizza-of-st-joseph/', 'http://www.steveedaniellehairandmakeup.com/', 'http://www.myhomegroup.com', 'http://all4you.cleaning', None, 'http://www.drkennedychiro.com', 'https://www.petsmart.com/stores/us/az/surprise-store1040.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', '1592174651', 'http://www.moestire.com', 'http://theartpartystudio.com/', 'https://www.handandstone.ca/locations/richmond-hill', 'http://www.smallcakesphx.com', 'http://www.ratatouillerestaurante.com', 'https://rosyeyebrows.com', 'http://www.phoenixcylinderhead.com', 'http://www.gobencars.com/', 'http://www.bellamiahairstudio.com/', 'https://www.hotelartskensington.com', 'http://www.qimontessori.com', 'http://www.AZbodySugaring.com', 'https://www.ceenta.com', 'https://www.firehousesubs.com/locations/nc/indian-trail', None, 'http://startersaz.com', None, None, 'http://pdubsbbqlasvegas.mypub.website', 'http://porterchiropracticaz.net', 'http://www.alexanderslv.com/', '1592174720', 'http://www.milestonesrestaurants.com/', 'http://www.eddiesalehouse.com/', None, 'http://www.xclusivesparlor.com/', 'http://www.christianjamesart.com/#!/page/183244/home', 'https://www.wyndhamhotels.com/hotel/49487?tel=18002521709&iata=00093785&cid=fe:ra:20170406:yl:pp:ramus:49487', 'http://www.torontomarriagecounselling.ca', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.asianimages.biz', 'http://www.sallybeauty.com', 'https://www.jeansflowers.org/?srccode=yelp_track', 'http://www.lassendasspineinstitute.com', None, 'https://locations.jackinthebox.com/us/az/chandler/900-n-cooper-rd', None, 'http://www.caplans.ca/', None, None, 'https://www.ewingirrigation.com', 'http://www.six02.com/scottsdale', None, None, None, 'https://internetmarketingteam.com', 'http://lucerestaurant.net', 'http://www.penn-station.com/', '1592174806', 'http://loandaodentistry.com', '1592174812', None, None, 'https://bmcmattress.com?utm_campaign=PhoenixJanMar2018&utm_medium=organic&utm_source=Yelp&utm_content=website-organic', 'http://www.homesurfacesaz.com/', 'http://thelivingroomhairstudio.com', 'http://www.lecreuset.com/stores/tanger-outlets-phoenix-glendale-az', 'http://clinicalsolutionsskincare.com', 'http://www.danier.com', 'http://www.hollisfamdental.com', 'https://drivingmba.com/?utm_source=Yelp&utm_medium=CPC&utm_campaign=Yelp-Ads', 'https://genkijapanese.info', 'http://www.contactlensking.com/', 'http://www.head2toessalon.com', None, None, None, 'http://americarestaurant.ca/', None, 'http://www.amresupply.com/locations/calgary', None, None, 'https://dekalash.com/find-a-studio/pennsylvania/wexford/', None, 'https://www.mjchristensen.com', 'http://www.pusateris.com', 'http://ProCS.us', 'http://swandetailing.com', 'https://ironglovesboxing.com/', 'http://www.bellunionautoservice.com', 'http://www.shoepalace.com?utm_source=yelp&utm_medium=yelp149', 'https://axethrowingpgh.com/booksouthhills/', 'http://www.tuttifruttidejeuners.com/en', 'https://www.courtesyjeepsuperstitionsprings.com', None, 'http://www.londoncleaners.com', None, 'http://www.helvighealth.com/', 'http://www.bebe.com', '1592174941', 'http://www.verizonwireless.com/stores/arizona/scottsdale/promenade-330170/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.lilliputhats.com/', 'https://www.number7honda.com', None, None, 'http://www.wineamplified.com/', 'http://www.glennstoolservice.com', 'http://www.thevictorianmonkey.com', None, 'https://fntarizona.com/scottsdale-kierland', None, 'http://www.anthemchildcare.com', 'http://www.nicols.ca/', 'http://blueskyoils.com', None, 'http://faceofanangel.net', 'http://www.intersport.ca', 'http://shessheik.com', None, None, None, None, 'http://www.adventcoworking.com', 'https://www.walmart.com/store/2512/phoenix-az/details', 'http://www.universalmotorcarslv.com', 'http://northpawdogs.com', '1592175027', 'http://www.pawsinthebath.com', 'http://www.auntieannes.com', 'https://www.walmart.com/store/2256/henderson-nc/whats-new', None, None, None, None, 'http://www.scavolinitoronto.com', 'http://holidaypetfestival.com', 'http://www.precisealterations.com', None, '1592175060', '1592175063', None, None, None, 'http://cateringcompanieslasvegas.com', 'https://www.wyndhamhotels.com/hotel/09499?tel=18003291073&iata=00065402&cid=fe:di:20161220:yl:pp:dius:09499', None, 'http://www.samosagrill.com/', 'http://www.lvcrystalnailspa.com', 'http://www.jamesgallery.net', None, None, 'http://www.thekentstage.com', None, 'http://noirtacgroup.com', 'https://www.goodyearmoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://yuriyscustomjewelry.com', None, 'http://www.vdevmaison.com', 'http://www.newprairieconstruction.com', 'http://www.parkroadhealingarts.com/', 'https://www.ecolinewindows.ca/location/calgary/', None, 'https://www.target.com/sl/mesa-west/1429', None, None, None, None, None, 'http://www.peterparvez.ca', None, 'http://www.teavana.com', 'http://www.lifecaremedicalrx.com', 'http://www.saladessensations.com', 'https://www.jerseymikes.com/3020', 'https://www.uneedmartialarts.com', '1592175182', 'http://aldi.us/index_ENU_HTML.htm', 'http://lincolndoor.com', 'http://bk.com/', None, None, 'http://designerartdirect.com', 'http://www.eljesseautorepair.com/', '1592175206', 'http://www.marriott.com/hotels/travel/yyzbp-fairfield-inn-and-suites-toronto-brampton', 'https://bolmergc.com', 'http://www.snapfitness.com', 'http://www.arrowheadlakesdentistry.com', 'http://www.simonesmtlebanon.com', 'http://www.jewelrysalonlv.com', 'http://www.whitehousechicken.com', 'http://www.carlitosmokes.com', None, None, 'http://www.riderscycleboard.com', None, None, 'http://www.conns.com/store-locator/nevada/las-vegas-89121', 'http://www.glowbeautyloungellc.com', None, 'http://www.sugarmarmalade.com/', None, None, None, None, 'http://scottsdalelavishnails.com/', 'http://www.bambooandspine.com', 'http://www.eyeglass-store.com', 'http://www.pioneercardiovascular.com', 'http://www.davisvillemedicalclinic.com', None, 'http://www.robbellplumbingservices.com', None, None, 'https://oralsurgerylv.com', 'http://www.ritzcarlton.com/en/Properties/Phoenix/Dining/Bistro24/Default.htm', None, None, 'http://envynailsspa.ca', 'https://happytreeslandscaping.com', None, None, None, 'http://kimmiesrestaurant.com', 'http://www.7thdegreeclothing.com', None, None, 'http://www.168sushibuffet.com/mississauga', 'http://www.chipofftheblocklv.com', None, 'http://www.ezpawn.com', 'http://www.applebees.com', 'http://www.portofsubs.com', 'http://www.thecharlotteforum.com', 'https://lastresrosasllc.yahoosites.com', 'http://www.amayaexpress.com/', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Phoenix-AZ-85023/858021/', None, '1592175367', 'https://agents.farmers.com/nv/las-vegas/yebel-escalona?SourceID=AMPALFYEAG&utm_source=Yelp&utm_medium=Local', 'http://buddysautorepair.com', 'http://www.mactechcomputer.com', 'http://www.azmountainviewmassage.com', 'http://vandykeaesthetics.com', None, 'http://www.faithfulwordbaptist.org', None, 'http://www.calgarylabservices.com/', 'http://onestoprealtylv.com', 'http://farmhousefoods.com/', None, None, 'http://koreangrillhouse.com/yonge-bloor-location/', 'http://rollinrustgarage.com', None, 'http://vintageconservatory.com', 'http://phatbuddhatattoos.com', 'https://www.241pizza.com', 'http://www.DentistryoftheCarolinas.com', None, 'http://www.rockstaraccountantsllc.com', 'http://www.chandleraz.gov/default.aspx?pageid=625', None, 'http://www.onemanandahammer.com', None, 'http://www.sushinotori.com', '1592175450', 'http://locations.harristeeter.com/nc/charlotte/205/', None, 'http://www.scriptpharmacy.ca/', 'http://www.pancheros.com/locations/urbana', 'http://www.cultivategoods.com', 'http://www.starbucks.com', 'http://www.reynoldsplumbingllc.com/', 'http://www.clevelandcupcakecompany.com/', 'http://www.esmil.com', 'https://www.destinationhotels.com/scottsdale-resort/dining/bar-six40', 'https://www.wwwilliams.com/location/phoenix-az/', None, 'http://www.quiktrip.com', '1592175489', 'http://paradisegreens.com', 'http://www.aerobatics.com', None, None, None, 'http://bellybombz.com/lasvegas', None, 'http://www.madtownrentals.com/', 'http://www.eyedistrictbyjo.com', 'https://www.bathandbodyworks.com/store-locator', None, 'https://www.zamzamhalalmeat.com', 'http://www.walmart.ca/en/walmart-meadowvale-supercentre/3054', None, None, 'http://www.perfectcredit60days.com', 'http://todaysauto.ca', None, None, None, 'http://stores.tuesdaymorning.com/nc/matthews/home-decor-matthews-nc-char0146.html', None, None, 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', None, 'http://www.tntwindowtint.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://galaxyktv88.com', 'http://www.hollandmarshsoupfest.ca/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.cellularsourcestore.com', 'http://aldi.us/index_ENU_HTML.htm', 'http://www.openstudioartcafe.com', None, None, '1592175611', 'http://www.haifengchinese.com', 'http://www.centennialpediatricslv.com', None, None, 'http://www.mississauga.ca/portal/discover/lakeviewgolf', 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'http://www.abceurodeli.com/', None, '1592175639', None, 'http://www.malkinlegal.com', 'http://www.nextlevelpaintersaz.com', None, None, None, '1592175656', 'https://www.centurylink.com', None, 'https://www.mytightface.com', None, 'http://www.suncoastaz.com/', 'https://www.indochino.com/showroom/charlotte', None, 'http://www.indulgeandco.com', None, 'http://tradeandlore.com', None, 'http://heartlandgsbeautybar.simplybook.me/sheduler/manage', 'https://www.emser.com', 'http://www.quiktrip.com/', None, 'https://www.smithsfoodanddrug.com/storeHours?store=70600376', None, 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', '1592175713', 'http://www.The-Dawg.com', 'http://www.southtempeapartments.com', 'http://shop.hobbylobby.com', 'http://www.thefitalterations.com', 'http://www.vpicasso.com', None, 'http://www.healingheartspeds.com/', 'http://sportsperformanceandspine.com', 'http://www.racewaychrysler.com', 'http://www.fendi.com/ii/store-locator', 'http://clickserve.dartsearch.net/link/click?lid=43700044280205718&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', '1592175749', 'http://www.barbqueboss.com', 'http://adjaafricanbraiding.com', '1592175758', 'http://beyondexpectationdental.com', None, 'http://www.petvethospitals.ca', 'http://www.azenaphoto.com', 'http://www.axisgear.ca', 'https://www.trebilcockcoffee.ca', 'https://www.thetouchofitaly.com', 'http://Rickslawnandlandscaping-lv.com', '1592175785', 'http://www.onceuponachildmacleod.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.espressoroyale.com/', 'http://dtrschooloftrucking.com', 'http://newoutlookopticalnv.com', None, 'http://sushi930.com', 'https://www.mediweightloss.com/locations/ballantyne?_ppc=Z8FWKRXKT5', None, 'http://www.richardsgardencenter.com', None, 'https://locations.levi.com/nc/charlotte/denim_charlotte_nc_258.html', 'http://mojoscoffeeandmore.com', 'http://www.barefootpoolman.com', 'http://www.lushexpress.com', None, 'http://www.stclair.org', None, '1592175848', 'http://www.palmettopethospital.com', 'http://www.mountainsidechiropractic.com', 'http://www.exclusiveballoons.com', 'https://diamondsstrip.ca', 'http://valleywidehouses.com', None, 'http://www.dayspring-umc.org', None, 'https://www.northtownvethospital.com', None, 'http://www.candy-addict.com', 'http://www.harthouse.ca', 'http://www.elitephoenixseo.com/', None, 'http://shea-blvd-chiropractor.com/', 'http://www.alluniformwear.com', None, 'http://www.draskovich.com', None, 'https://lvcollectables.com', 'http://jonesmoverz.com', None, 'http://www.gobeautybar.com', None, 'http://calgary.regency.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_calrc_en_homepage_desktop&code=YB', None, None, 'http://www.thesundanceclinic.com/', 'http://www.sunvalleyfamilyoptometry.com', 'http://www.vipbeautysalon.org', 'http://www.murdockmeals.com', None, 'http://www.pghfilmmakers.org', 'http://pferguson.pillartopost.com', None, 'http://www.dunkindonuts.com', None, None, None, None, 'http://www.masterpieceescapes.com', 'https://nothingbundtcakes.com/bakery/AZ/goodyear?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=goodyear_138', 'http://www.bobbiepinbeauty.com', 'http://www.firkinpubs.com', 'http://murphyusa.com', 'http://Swanpizza.com', 'http://www.advancedpreventivemedicine.com/', 'http://www.starbucks.com/store/6597/', 'http://www.infinityhd.tv', 'http://www.starbucks.ca', 'http://www.lasvegashomewatchers.com', 'http://torontopawn.ca', '1592179247', 'http://www.vegasdiscountnutrition.net', 'http://www.bulkbarn.ca/en-ca/index.html', 'http://adventuredogpark.com', 'http://www.timhortons.com/ca/en', 'http://www.apple.com/retail/southpark', 'http://www.iltartufo.ca', 'http://www.hydrotherapiesplus.com/', 'http://www.desertspringschiro.com', 'https://www.pizzahut.ca/store-details/store-R42101/pizza-hut-Etobicoke', 'http://www.thetirexpress.com', 'http://www.tuckedawaycraftkitchen.com', 'http://www.renewedlifechiropractic.com', 'http://www.phxplastering.com', None, None, 'http://www.muchoburrito.com', 'http://www.theriverwoodconservancy.org/', None, None, None, 'http://blackforgecoffee.com', 'https://www.slatescottsdaleapartments.com/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://locations.dennys.ca/AB/CALGARY/248179', None, 'http://www.babysafehomes.com/united-states-baby-proofing-locations/child-proofing-phoenix-arizona', 'http://www.clevelandmoto.com', 'http://www.applerepaircanada.ca', 'https://www.druryhotels.com', 'http://www.sabaiaz.com', None, 'http://www.sunsationalswimschool.com/', 'http://www.lapetgrooming.com', 'http://www.gamestop.com/store/us/az/scottsdale/2760/sonoran-village-gamestop', None, 'http://www.ezyes-takeout.com', None, 'http://www.trendvape.com', 'https://glassnickelpizza.com/location/sun-prairie/', 'http://www.arizonarvresorts.com/Pioneer', None, '1592179997', 'http://www.myhealingplaceaz.com', None, 'http://www.restaurantconfluence.com', None, 'http://www.bioprollc.com/', 'http://www.valleyofthesunpharmacy.com', 'http://www.arizonasandwichco.com', None, 'http://www.frogbox.com/toronto', 'https://sushisanrestaurant.business.site', 'http://www.jwoodflooring.com', 'https://www.lefrancisstudios.com', 'http://www.aboutudental.com', 'http://www.kokomogrills.com', 'http://www.ivanhairsalon.ca', '1592180030', None, 'http://www.granadalakestempe.com', 'http://www.capellaeyecare.com', None, None, 'http://www.onthelistdenver.com', None, 'https://www.lvscc.com/south-rancho', 'http://www.lotsmartsolarscreens.com', 'http://www.ontariotrails.on.ca/trails/view/cheltenham-hills', 'http://georgesbrasserie.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://freshandeasy.com/', None, None, 'http://www.northwoodslanes.com', 'http://cleanmycarpetlv.com', 'http://www.nonnispizzamenu.com', None, 'http://globalbikes.info/', 'https://locations.wendys.com/united-states/az/phoenix/9905-w.-camelback-rd.', '1592180077', None, '1592180081', 'http://www.hotdogonastick.com', None, 'http://www.luchitas.net/elyria.php', None, None, None, 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', None, None, 'https://www.fitnessworks.com/locations/dobson-rd-chandler-blvd', None, None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.buckysportabletoilets.com', None, None, 'https://www.mirage.com/en/restaurants/osteria-costa.html', 'https://www.cheyennedentalgroup.com/?utm_source=yelp&utm_medium=link&utm_campaign=yelp', 'http://www.atobmove.com', 'https://locations.waxcenter.com/nc/charlotte/charlotte-arboretum-0169.html', None, None, 'http://www.phoenixpubliclibrary.org/Locations/Pages/Yucca.aspx', None, None, 'http://www.qsdiner.com', 'http://www.pb.com', 'http://www.amenzone.com', 'http://www.cremacoffee.ca', 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpsouthwestorganic', 'http://www.blueberryhillrestaurants.com/', 'http://www.wishacake.ca', 'http://www.littlecrittersvet.com', 'http://www.c3lasvegas.com', '1592180154', None, 'https://www.thebrick.com/pages/store-north-york', 'http://www.rightc3.com', 'http://imboardgames.com', 'http://www.bwilliamsdds.com', 'http://www.stephita.com/', 'http://www.underdogpetrescue.org', 'http://www.canadianamphitheatre.net/', 'http://www.anthropologie.com', 'http://www.noblecare.us/', None, None, 'http://titanhomeimprovements.com', 'http://nvjawdoc.com/', 'https://www.redlobster.ca/locations/list/on/brampton/368-queen-street-e', '1592180189', None, 'http://www.scottsdale-sc.com', 'http://www.zappos.com', 'http://www.naturalgourmetfoods.com/', 'http://www.walgreens.com/locator/Walgreens-10503-W-Thunderbird%2C-Suite-101B-Sun-City-AZ-85351/id=10018', None, '1592180205', 'http://www.pittsburghcitywide.com', None, 'http://www.inspectioneeringpgh.com/', 'http://www.arizonacharliesboulder.com/Food-Drink/Sourdough-Cafe', 'http://www.regency.edu/campus/madison/?guest', None, 'https://www.leprovencalbistro.com', '1592180219', 'http://www.fallasstores.com', None, 'http://sabiskitchen.com/', 'https://www.nofrills.ca/store-locator/Enzo%27s+nofrills+%28Yonge+St.%29/0770?storeId=0770', 'http://www.sassiskin.com', '1592180232', None, 'http://www.kyrene.org', 'https://www.aqualineplumberselectriciansacrepairscottsdaleaz.com', None, '1592180244', None, None, 'https://bananarepublic.gap.com', 'http://www.artisticintegrity.ca', 'http://www.plumberphoenixboydco.com', '1592180257', 'http://www.goldengeckocoffee.com', None, 'https://www.kfc.ca/store/3199-blvd-taschereau-greenfiled-pk', 'http://www.carolynannryan.com', 'http://www.hyperproductionsdjs.com', 'http://www.menchies.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.coldstonecreamery.com/stores/20030', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.globalpetfoods.com', 'https://www.nbc.ca', None, 'https://www.maids.com/106/?utm_source=Yelp', 'http://www.preferredhomecare.com/', 'http://www.lighthouseNMT.com', None, 'http://www.coiffeurssalon.com', None, 'http://www.ganleywestsidehyundai.com', 'http://www.marcsimonlaw.com', None, 'https://www.lamaithaicuisineaz.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=1943&localechange=1', None, 'http://www.currentdentallasvegas.com', 'http://www.coupebizzarre.com', None, 'http://hallfamilyfarm.com/', 'http://www.ohiyo68.com', 'http://www.knuckleheadstobacco.com', 'https://www.livingspaces.com/stores/phoenix', None, 'http://aldi.us/index_ENU_HTML.htm', 'https://www.prestigecleaners.com', '1592180331', 'http://www.allwashedwindowcleaning.com', 'http://www.chiropractichealthmatthews.com/', 'https://www.phxrisingfc.com/stadium-information', 'https://www.ritasice.com', 'http://logansroadhouse.com', 'http://bluetruckwindowcleaning.com', 'https://restaurants.applebees.com/az/tempe-88083.html?utm_campaign=Local&utm_medium=Display&utm_source=Yelp', 'http://moonlitetavern.com', 'http://www.fiveguys.com', None, 'http://www.HealthyOutlookFamilyMedicine.com', 'http://www.fresh52.com', 'http://www.meckneurology.com', 'https://www.erieinsurance.com/about-us/locations/charlotte', 'https://www.rosewoodcandlebar.com', 'http://www.lvzendog.com', None, 'http://www.centralazsupply.com', 'http://www.costco.com/warehouse-locations/henderson-nv-673.html', 'http://www.coldstonecreamery.com/stores/20030', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, None, 'https://www.revampextensions.com', 'https://breezemassage.wixsite.com/85301', 'http://www.costcutters.com', None, 'http://www.rodefshalom.org', 'http://www.haychiro.com', None, 'http://www.nailsupspahuntersville.com', 'http://fountainhillsbowling.com', '1592180403', 'http://azmrfixit.com/', 'https://probateattorneyvegas.com', 'http://www.siegelsuites.com/rent-apartment-las-vegas/paradise-las-vegas-apartments.php', None, None, 'http://www.shopthemensroom.com', None, None, '1592180420', 'http://www.lilbaci.com', 'http://www.toronto.ca/parks/prd/facilities/complex/1099/index.htm', None, None, 'https://ezautosaleslv.com', 'http://www.dmscshea.com', 'https://haircutmenbillgreenpittsburghpa.com', 'http://www.dentalcaretoronto.com', None, None, '1592180441', 'http://www.mirrorbombstudio.com', 'http://www.2020visionphotos.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YULMV', None, 'https://www.tgifridays.com/locations/1110/fridays-robinson-pennsylvania', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYZTS', 'http://www.annalakshmi.ca', 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://lvcraftshows.com', None, 'http://ktran1401.wix.com/pamperednailsalon', None, None, 'http://www.poolman.com', 'https://www.travelex.com/stores/phoenix-sky-harbour-international-airport-terminal-4-checkpoint-b-phoenix-az/7283', None, 'http://oldnavy.gap.com/customerService/store.do?storeid=6528', None, None, 'https://www.cantina15eleven.com', None, None, 'http://locations.truereligion.com/az/scottsdale/51049/', 'http://www.nolldentistry.com', 'http://www.annexales.com', 'http://dekra.us/en/nevada/las-vegas-6020-n-decatur-blvd/', 'http://www.swanksalon.info', 'https://visionsource-loepervisionteam.com', 'http://hoopssportsbar.com', 'http://www.ArgonPest.com', None, None, None, 'http://www.arizonainterlocks.com/tempe', 'http://www.MellonsPub.com', 'http://arichtreatments.com', 'http://www.deserttailsanimalclinic.com', 'http://www.billsbarandburger.com/venues/pittsburgh/', '1592180530', 'http://www.hcxcharlotte.com/carmel-commons-hair-salon/', 'https://bignons.com/s-tryon-location', '1592180537', 'https://nothingbundtcakes.com/bakery/NC/charlotte?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=charlotte_145', None, 'https://stjudesranch.org/', 'http://www.graciebarra.com/phoenix-az', 'https://www.outback.com/locations/oh/cuyahoga-falls', 'http://www.pizzapizza.ca', 'http://www.eatatfellinis.com/', 'http://www.santurbanospa.com', 'http://www.theartofshaving.com', None, None, 'http://www.sugarpeony.com', 'https://www.lifecelebrationpetcrematory.com', 'http://www.hassanphoto.com', 'https://www.littlejohnslawns.com/', 'http://www.tiptoptrough.com', None, None, None, 'https://www.sephora.com/happening/stores/pittsburgh-shadyside', 'http://clevelandcinemas.com/location/6347/Chagrin-Cinemas-Showtimes', 'http://www.lifetimeeyecarecenter.net', None, '1592180585', 'http://www.wetseal.com', 'http://www4.ncsu.edu/~jtdemars/theshakeshack.html/', 'http://www.usfries.com/', 'https://www.carx.com/madison/5633-odana-rd/', 'http://www.ihg.com/staybridge/hotels/us/en/madison/msnhc/hoteldetail', 'https://siennajewelsalon.com', 'https://andersonsdelivery.com', 'http://www.azwood.com/', None, '1592180608', 'https://www.sunbaraz.com', 'http://www.splishsplashpools.com', 'http://www.swisschalet.com', 'http://www.hutchsbicyclegarage.com', None, 'https://www.levinfurniture.com/furniture-store/oh/solon/6130-kruse-drive', 'http://waternicetempe.com', 'http://lafontanagelati.com/', None, 'https://www.honorhealth.com/locations/primary-care/honorhealth-medical-group-jomax?utm_source=yelp&utm_medium=local&utm_campaign=honorhealth-medical-group-jomax', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', '1592180634', 'http://www.mezes.com', 'https://www.crystalglass.ca/location/calgary-south', None, None, 'http://bikebarnaz.com/', None, None, 'http://www.tashabradyphotography.com', None, 'http://www.sunrisecarpetupholsterycleaning.com/', '1592180654', 'http://www.geniecarwash.com', 'http://www.phoenixlocksmithoncall.com', 'http://www.bronzfx.com', None, 'http://www.urbancurls416.com', 'http://www.einsteinbros.com/', 'https://www.chick-fil-a.com/surprisemarketplace', None, 'http://www.andrewblairs.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.caferio.com/', 'http://spencerstv.com', 'http://www.cuttlefishscottsdale.com/', 'https://www.terragreenhouses.com/terra-milton-garden-centre', 'http://www.performanceext.com', None, None, 'http://charlottenc.gov/cats/rail/lynx-blue-line/Pages/parkwood-station.aspx', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.cinemark.com/nevada/century-16-south-point-and-xd', 'http://www.bgchenderson.org', 'http://popeyeschicken.ca', None, 'http://www.shanghaiwokbyby.com', 'https://www.phoenixmechanicshop.com', 'http://www.mysichuanpalace.com', None, 'http://www.lowes.com', 'http://www.extremepestcontrolLasVegas.com', 'https://www.questdiagnostics.com/home/patients?utm_source=yelp&utm_medium=social&utm_campaign=pscprofiles&utm_term=psc&utm_content=patients', None, 'http://www.sidernobakeryllc.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://www.wolbertautobody.com', 'http://www.mscarolsgymkids.com', None, 'https://www.redlobster.com/locations/list/nc/concord/8012-concord-mills-blvd', 'http://www.crazydaisieslv.com', 'http://abbeyroseflorist.com', 'https://positive-movement-logistics.business.site', 'http://www.delaneyauction.com', None, 'http://www.freakstattooemporiumnv.com', 'https://www.oxifresh.com/locations/nc/charlotte-carpet-cleaning/?utm_source=yelp&utm_medium=social&promo_code=YP5000', None, None, None, 'http://www.alnoorkebab.com', None, 'http://www.avalondentistry.ca/', 'http://jwoodsonderm.com', None, None, 'http://www.palmcleaningsystems.com/wp/', None, None, None, 'http://www.innovativevapors.com', 'http://www.naturalbeautyhairboutique.com', 'http://www.bethelbarbershop.com', 'http://www.livescanlasvegas.com', None, 'https://hotelxtoronto.com/en/falcon-skybar.html', 'http://www.danielsdiscount.com', 'http://www.thesmilecreators.com', None, None, None, None, 'http://www.koolthairestaurant.com', None, None, 'http://www.cowboycooling.com', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', '1592180808', 'http://www.jimpeplinski.ca', 'https://www.avis.ca/car-rental/location/CAU/CA/PQ/Dollard-des-Ormeaux/PCQ', 'http://www.vasilis-yyc.com', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.avecpanacherestaurant.com', 'http://www.shell.com', 'https://www.creativekidslearningcenter.com/schools/las-vegas-nv-6705/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhancedprofile', None, None, '1592180834', 'http://www.eatrastapasta.ca', 'http://www.chmuseums.org', 'http://www.settlersridgepa.com/', 'http://www.rightgear.net', 'http://www.bodyrevolution.net', 'https://istanbulsofra.com', 'http://www.3riversartsfest.org/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/32331+North+Scottsdale+Road-Scottsdale-AZ-85262/storeid=7839?cid=ps_ylp_2020', None, None, 'http://www.nvcoin.com', 'http://specialtyrvaz.com', 'http://www.azultimatechiropractic.com', 'http://www.moldanddefectlawyer.com', None, 'http://www.ultrasmoothskin.com/', 'http://www.tbmelectriclasvegas.com/', None, None, None, 'http://www.imperialpalace.com/casinos/imperial-palace/restaurants-dining/ginseng-3-detail.html', 'http://www.ventureoutrvresort.com', None, None, 'http://smittysresidentialpainting.com', 'http://royalthaihakka.com', 'http://www.instantac.com', None, 'http://www.rawfitnesslv.com/summerlin.html', 'https://calgarymovers.net', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89084/600-in-north-las-vegas/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-600&utm_content=website-link&howheard=IYE', None, None, 'http://www.cobrinhabjjlasvegas.com', 'http://www.rooterranger.com', 'https://www.ladym.com', 'http://www.doubledouble.ca', 'http://www.orleanscasino.com/entertain/bourbon-street-cabaret?disid=wmm_yelp_to_corporate_bourbonstreetcabaret_organiclink', None, 'http://pawncorp.com', '1592180934', 'http://www.visionexpress.ca', 'http://www.mashawiaz.com/', 'https://www.pearsoneyecare.com/location/superstition-springs-mall-mesa/', 'https://trivenisupermarket.com', 'https://leader-barber-style-shop.business.site', 'http://www.unclesmoke.com', None, 'https://www.lasvegasbouquet.com', None, 'http://sachisalon.com', 'http://www.bixelsstudios.com', 'http://www.hairsalonlulu.com', None, 'http://www.thriftypropane.com/', 'http://www.balloonatix.com', None, None, 'http://www.starbucks.com/store/9298/', 'http://mississaugaemission.ca', 'http://www.dirtyat1230.com', None, 'http://www.11BravoMobileAuto.com', 'http://www.lagoeastbank.com', None, 'http://www.vitabellasalonandspa.com/', None, 'http://www.climatechangeyyc.com', 'http://fingerprintingink.com', 'http://www.oudejansinteriors.com', None, 'http://www.japco.ca', None, '1592181015', 'http://www.explace.on.ca', 'http://www.kensautorepair-hub.com', 'https://shop.nordstrom.com/store-details/nordstrom-scottsdale-fashion-square?utm_source=yelp&utm_medium=organic&utm_campaign=fls&utm_content=380&utm_channel=lcl_brand_p&sp_source=yelp&sp_campaign=fls', 'http://www.sfagentonline.com?cmpid=FVUJ_BLM_0006', None, 'https://www.aqua-tots.com/ahwatukee/', 'https://myhoneybakedstore.com/charlotte/114', None, 'http://phoenix.gov/parks', None, None, None, 'http://www.dryaged.ca', None, 'http://www.cpk.com/Location/Details/Ross-Park', None, 'http://www.chavezboxinggym.com', 'http://www.curvyconsignments.com', None, None, 'http://www.swlegalgrp.com/', None, None, 'http://www.superstore.ca', None, 'http://www.luxor.com/amenities/amenities_the_spa.aspx', 'http://chucksroadhouse.com', None, None, 'https://www.restaurant-mesa.com', 'http://www.gap.com/products/westlake-oh-store-7181.jsp', 'http://www.gotitcoverednv.com', None, 'http://www.ihg.com/holidayinnexpress/hotels/us/en/mentor/mntoh/hoteldetail', None, None, None, None, 'http://nanadeesdiner.com', 'http://shopping.schubachstore.com/', None, None, 'https://aarons-ark-mobile-veterinary-services.business.site', None, 'http://www.eldoradocasino.com/dining.cfm', 'http://www.commutehome.com/', None, 'http://www.badgergymnastics.com', 'http://www.hightvet.com', None, 'https://www.wedgewoodweddings.com/venues/arizona/palm-valley?utm_source=yelp&utm_medium=social&utm_campaign=palm-valley-yelp', 'http://Inglewoodpizza.ca', 'http://www.gianteagle.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.boulangerielefournil.com/', 'https://www.walmart.com/store/4148/charlotte-nc/details', 'http://www.byrdspub.com', None, 'http://www.headwaystudio.com', 'http://www.bronzecafe.com', None, 'https://druxys.com/location/2-st-clair-ave-colonia-place/', 'https://www.choicehotels.com/arizona/phoenix/sleep-inn-hotels/az140/rates', 'http://www.alcornhair.com', 'http://www.topshotlasvegas.com', None, 'http://www.bigmouthluckdumplinghouse.com/', 'http://www.matsudasushi.com/', None, '1592181177', 'http://nile-seafood-market-restaurant.business.site', 'http://versatileautoappearance.com', 'http://www.pizzahut.com/', 'http://www.walmart.ca/en/richmond-hill-supercentre/3195', None, 'https://attorneysforfreedom.com', 'https://havensmedispa.com', 'http://www.bannerhealth.com/locations/glendale/banner-physical-therapy-eugie?utm_source=GMB&utm_medium=Listing&utm_campaign=PT%20WebCTA', 'http://www.allproawninglv.com', None, 'http://www.woodbinetoyota.ca', None, 'http://www.ihg.com/holidayinnexpress/hotels/us/en/calgary/yyccg/hoteldetail', 'https://sukiesbridal.com', None, 'http://green-pepper-ot-xanh-asian-cuisine.business.site', 'http://www.sodadispenserdepot.com', 'http://www.7-eleven.com/?yelp=36121', 'http://www.medusaslv.com', 'http://www.cozzeria-pizzeria.com', 'https://www.alanhuirealty.com', 'http://www.clevelanderbar.com/', 'http://www.streamersicecream.com/', 'http://www.fraziersbarbershop.com', None, 'http://www.mufflermasters.com', None, 'https://functionbar.ca', 'http://worldsalon.ca', 'http://www.PetLossAtHome.com', 'http://www.summerlindance.com/', 'http://voxcurvy.com', 'http://www.paintingbyhector.com', None, None, 'https://marsautoservice.net', 'https://www.wyndhamhotels.com/hotel/08797?tel=18007606483&iata=00093785&cid=fe:tl:20170523:yl:pp:tlus:08797', None, 'https://locations.paychex.com/us/pennsylvania/pittsburgh', 'http://www.ymcacharlotte.org', 'https://www.chandlerair.com', 'http://www.poshmommy.ca', '1592181276', None, 'http://www.beancurd.biz', 'http://hummusfactorylv.com', 'http://gilberttowncommons.com/?utm_campaign=YelpWebsite&utm_medium=YelpBusinessProfile&utm_source=Yelp', 'http://www.starloancenters.com', 'http://www.pnc.com', 'http://skincarecleveland.com/index.html', None, 'https://www.kalologie-lasvegas.com', None, None, 'http://www.westlibertycycles.com', 'http://www.marriott.com/hotels/travel/phxcs-springhill-suites-phoenix-chandler-fashion-center/', 'http://Chagrin-Falls.certapro.com/?source=Yelp', 'http://www.keepitcut.com', 'https://www.lugayfamilydental.com', 'http://k-momo.com', 'http://www.executivelounges.com', 'http://www.trulyengravables.com', 'http://www.ecodryrestoration.com', 'https://www.target.com/sl/arcadia-crossing/950', 'http://www.hobbylobby.com', 'http://www.hubnest.com/', 'http://fandombar.com', None, None, None, 'http://www.gianteagle.com', 'https://www.lasvegas-propertymanagement.com', 'http://www.boxheartgallery.com', 'http://corneaaz.com', 'http://www.aveda.com', 'http://www.dralbertli.com', 'http://www.thegatewaybarandgrill.com/', 'http://www.meckabc.com', None, 'http://sugarshackrecords.net', 'http://www.starbucks.com/store/89998/ca/vmr-lucerne/2362-chemin-lucerne-ville-mont-royal-qc-h3r-2k5', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', 'http://www.bennysbar.net', 'http://www.ringaudio.com', None, 'http://dlautomotive.com', 'http://401dixieinfiniti.ca/', 'http://www.operationhalloween.com', 'http://www.fetchpetcare.com', 'http://bluebirdcarpet.com', 'http://auclv.vegas', 'http://www.coachcanada.com/coachcanada/ss.casino.asp', 'http://www.novellenail.com', None, 'https://ad.doubleclick.net/ddm/clk/414776926;215768644;y', 'https://www.apexskin.com/locations/solon-oh-dermatology-office/', 'https://vyiannibas.wixsite.com/juliana', '1592181407', None, 'https://ca.louisvuitton.com/fra-ca/magasin/canada/louis-vuitton-montreal-ogilvy?campaign=b_yelp/storepage', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700007898397760&ds_s_kwgid=58700000649767852&ds_e_adid=%7Bcreative%7D&ds_url_v=2&cmpid=ADV_PG_%5B*KeywordID*%5D', 'https://Scottsdalequarter.com', 'http://www.healthpalace.ca', 'http://www.aamcogilbertchandler.com', None, 'https://www.hungryhowies.com/store/hungry-howies-01823?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=1823&utm_content=Website_Link', None, 'http://www.generate.to', None, 'http://campagnolotoronto.com/', '1592181442', 'https://www.24hourfitness.com/gyms/las-vegas-nv/silverado-las-vegas-sport', 'http://www.captainscovenc.net/', 'http://sanctuaryongreen.com/', 'http://www.nulawn.net', 'https://www.simonmed.com/locations/all/simonmed_imaging___greenfield', None, None, None, 'http://www.papajohns.com', None, 'http://restaurantgalleria.ca/fr/', None, 'http://www.sbcfoods.com/', 'https://freshfixofheights.com', 'http://www.myautoamerica.com', None, 'http://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLEEM', 'http://www.fonda-las-cazuelas.com', 'http://zaxe.ca', 'http://www.jmphoenixcriminalattorney.com/', None, 'http://www.aztrailstravel.com', 'http://www.allstartaxi.ca', 'http://www.autobell.com/ab_locations/333-n-new-hope-rd/', 'https://stopandshop.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.bergamotmassage.com', 'http://rossispizzamonona.com/', 'http://www.lakeeriemonsters.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Las-Vegas-NV-89128/027192/', 'http://go.georgestreetphoto.com/l/9752/2014-06-04/m1c3t', None, 'http://www.danspoolcare.com', 'http://www.earlycollegenv.com', 'https://www.oliversplumbing.com', 'https://www.lowes.com/store/AZ-Surprise/1607?cm_mmc=YEXT-_-SiteLink-_-1607-_-Lowes', 'https://stores.guitarcenter.com/avondale?source=4GOA5AJBB', 'https://www.perfectteeth.com/office/az/surprise/85379/waddell/', 'http://www.conciergemakeup.com', None, 'http://soilextractors.com', 'http://greengarageaz.com', '1592181555', None, 'https://www.apparelprousa.com', None, 'http://www.adamahmadison.com', None, None, 'http://www.dieselworldwide.ca', 'http://heritagetattoolv.com', None, 'http://www.phoeniximprovfestival.com', None, 'https://www.cosmeticlasercenters.com', None, 'http://www.zapitwash.com', 'http://therocksportsbarandgrille.com', 'https://www.sprint.com/storefronts/bd/sprint-phoenix-az-85037-d-4610/', None, 'http://www.taverninthehills.com', 'https://dream-cut-barber-and-stylist.business.site', None, None, 'http://www.solsticesunglasses.com/', None, None, 'http://www.patisseriefleur.com', '1592181622', 'http://locations.michaels.com/AB/CALGARY/3902/', 'https://www.bestbuy.ca/en-CA/stores/store-locator.aspx?StoreID=62', 'http://www.kristenmarieweddings.com', 'https://www.eatnpark.com', 'http://www.middletonpower.com/', 'http://www.lakeviewautopartsinc.com', 'http://www.avedamontreal-lifestyle.com', 'https://www.laplazataqueria.com', 'http://discountfloorsaz.com', 'https://www.bannerhealth.com/locations/mesa/banner-urgent-care-1', 'https://www.shopfuego.com', None, 'https://www.labl.ca', None, None, 'http://www.cortezindustriesllc.com', None, 'http://www.skilletsforbreakfast.com/', None, None, 'http://lvfurnituredirect.com', 'https://www.petalsofloveflorist.com', 'https://www.aairofcharlotte.com', 'http://launchhouse.com/', None, None, 'http://www.friendlys.com/', None, 'http://american1stheating.com', 'http://chase.com', '1592181697', 'http://www.bcbg.com', 'http://www.signaturerentalsbyowner.com', 'http://www.traditionalstitches.com/', 'https://www.supercuts.com/locations/az/peoria/north-valley-power-center-haircuts-82958.html', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.mixxiemixologist.com', 'http://carolinawinesandspirits.com', None, 'http://www.altf.com', 'http://www.classiccarspa.com', None, 'https://palmbeachtan.com/locations/AZ/Tempe-East-Broadway-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'http://www.trustedepa.com', None, '1592181735', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', '1592181744', 'https://www.activedecorating.com', 'http://www.TheWomansCenter.com', None, 'http://moderneraweddings.com', 'http://www.mrdetailohio.com', 'http://winginout.com', 'http://www.bigotires.com', 'https://superiorplay.com/dealerlocator/north-carolina/charlotte', 'http://www.bk.com', 'http://www.lasvegasvasectomy.com', 'http://www.wildbunchdesertguides.com', '1592181773', None, None, 'http://avonurgentcare.net/', None, None, 'http://www.mimiscafe.com', 'http://tenrenstea.com/start/', None, 'https://santafestation.sclv.com/gaming/sports-book?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.look-stylesociety.com', 'http://www.callsp.com', 'http://www.datadoctors.com/locations/101', 'https://cbdemporium.com', 'http://www.ledolci.com/', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://www.marriott.com/hotels/hotel-information/fitness-spa-services/details/phxcb-jw-marriott-scottsdale-camelback-inn-resort-and-spa/5014642/', 'http://www.cocokala-lasvegas.com', None, None, None, '1592181829', None, 'http://www.twintranslations.com', 'http://www.target.ca', None, None, 'http://www.proximityatpapago.com/index.aspx', 'https://www.massageaddict.ca/calgary-sagehillcrossing/', 'http://www.donaldjpliner.com', None, 'http://bombatacos.com/fairlawn-oh', 'https://www.vitbeo.com', 'http://lanierparking.com/', 'http://SellWithOne.com', 'http://www.phoenixtitleloan.com/', 'https://www.eyesonhayden.com', 'http://CATCh.theater', 'http://www.goldenharboronline.com', 'https://www.kohls.com/stores/az/gilbert-621.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.nuturfofarizona.com', 'http://www.topgearcarwash.net', 'http://www.sansotei.com', None, 'https://www.walgreens.com/locator/walgreens-2324+w+war+memorial+dr-peoria-il-61614/id=6408', None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.bestbuyflooringcenter.com', 'http://www.flowerchildvintage.com/', 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', None, 'http://www.theglassguru.com/scottsdale/', 'http://www.clevelandrockgym.com', 'https://jessebrowns.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://www.colossalcupcakes.com', 'http://www.phoenixpediatrics.com', 'http://www.klearlykleaned.com', 'http://811kitchenbarlounge.com', 'http://www.blacklanterntattoo.com', None, 'http://www.dedicatedaudio.com', 'http://www.flipsideburger.com', None, 'http://www.teamorthodontics.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.appleone.com/?yelp_track', 'http://www.confectionarycupboard.com/', 'http://www.neworientalrecipes.com', None, None, None, 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', None, 'http://www.beckhamspub.com', 'http://www.7-eleven.com/?yelp=29644', 'http://www.goldentrianglebike.com', None, 'http://www.wildsagert8.com/', None, 'https://www.grifolsplasma.com/en/-/mesa-az', 'http://www.handsoncharlotte.org', 'https://blackbeardiner.com/location/las-vegas-tropicana/', 'http://www.resumerick.com', 'https://locations.davidstea.com/on-thornhill-17', 'http://www.trinitybellwoods.ca/', 'http://www.threes-company.com', None, 'http://www.braidyjewelers.com', 'https://acrirlty.com', None, 'http://popeyeschicken.ca', 'http://www.aactionmovers.com', 'http://www.lovhairbymarianne.com', 'http://www.pinklime.com', 'http://www.hanshiktaco.com/', 'http://www.littlecaesars.com/', 'https://local.firestonecompleteautocare.com/nevada/las-vegas/3770-s-maryland-parkway/', None, None, 'http://www.precisionguitaraz.com', 'http://www.elitehomeinspections.us', None, 'http://www.vantageloftslv.com/#Home', None, 'https://makeupbyalmah.business.site', 'http://www.salutelounge.ca', 'https://arizonaurologyspecialists.com/contact-scottsdale-thompson-peak', 'http://www.starbucks.com/store/11823/', 'http://www.azmobilereflash.com', 'http://www.baskinrobbins.com', None, 'http://www.fye.com', 'http://www.ampm.com', None, None, 'http://www.nygh.on.ca', 'https://sheridannurseries.com/store-locations/toronto-garden-centre/', None, 'http://www.weathervaneplayhouse.com', None, 'http://www.littleotterswim.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.ebtfloral.com/', 'https://bostonpizza.com/en/locations/sunridge.html', None, 'http://www.sayteaonbloor.com', 'http://www.anewtable.ca', 'http://www.bathurstbowlerama.com/', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/109+Dabney+Drive-Henderson-NC-27536/storeid=7055?cid=ps_ylp_2020', 'http://www.lesleyscreativecakes.com', None, None, 'http://www.gandermountain.com', 'https://housedoctoraz.com', 'http://www.greatclips.com/', None, None, 'https://locations.cariboucoffee.com/az/phoenix/2080-w.-northern-ave.html', None, 'http://oriondetailing.co', 'https://business.google.com/website_shared/launch_bw.html?f=vegas-noodle-house.business.site', None, 'http://www.southernpawsanimalhospital.com', 'http://www.pnpkaz.com', 'http://www.eventprostrategies.com', 'http://www.penn-station.com/westvirginia/', '1592182138', None, 'http://www.bohme.com', 'http://www.fatzombietattoo.com', 'http://www.globalmarketretail.com', None, None, 'https://www.wyndhamhotels.com/hotel/28120?tel=18885951878&iata=00093785&cid=fe:mt:20180223:yl:pp:MTUS:28120', '1592182158', 'https://www.amctheatres.com/movie-theatres/phoenix/amc-westgate-20?utm_uid=yelp', None, 'http://Www.piedmontvets.com', 'http://www.chachago.ca', 'http://rebelluxeaz.com', 'https://www.kingdomplumbing.com', None, 'http://www.sincitypc.com', 'http://www.weprintwhatyouwant.com', None, 'https://ballantynecleaners.com/drop-store', None, None, 'http://www.fastfreshfoods.ca/', 'https://comfortcare.ca', 'http://www.calgary.ca/CSPS/Parks/Pages/Locations/SW-parks/North-Glenmore-Park.aspx', None, 'http://www.dontbebroke.com/?utm_source=Yelp&utm_medium=Location%2BPage&utm_campaign=Yelp', 'http://bobochinabuffet.com/', '1592182216', None, 'http://www.quiznos.com', 'http://www.bolocakery.com', 'http://benvenutos.com/locations/middleton', 'http://yourvalleyproperty.com', None, None, None, 'http://www.mehowey.com', 'https://www.alfredoshairsalon.com', None, 'http://www.flooptical.com/index.html', 'http://www.fineskincare.ca', 'http://www.iautocars.com', None, None, None, 'http://www.bk.com', '1592182267', 'https://www.walgreens.com/locator/walgreens-1801+philo+rd-urbana-il-61802/id=11368', None, 'http://www.closetworld.com', 'http://www.chicsincity.com', 'http://www.terribleherbst.com/', 'http://www.altardstate.com/', None, None, 'http://www.madisonpubliclibrary.org/monroe-street', None, 'http://www.corekitchenaz.com', None, 'https://stores.jcpenney.com/nv/henderson/clothing-stores-henderson-nv-2626.html', 'https://gymvmt.com', 'http://www.nynyhotelcasino.com/entertainment/bars/bar-at-times-square.aspx', 'http://www.symdonchevy.com/?cs:pro=repman&cs:e=yelp', 'http://www.dgapplianceandair.com', None, None, None, None, None, None, 'http://imageeyecarenv.com', 'http://www.mondaynightauction.com/', None, None, 'http://www.pool-spaoutlet.com', 'https://ameritekusa.net', 'http://www.nepps.net/contact-us', None, 'http://www.diamondcharlotte.com/', 'http://www.caferumba.net/', 'http://www.libertystationtavern.com', 'https://surrealnightlife.com/las-vegas/', None, None, 'http://7eleven.ca/store-locator/33259', 'http://www.thestretchdoc.com', None, 'http://www.drumandmonkey.ca/', None, 'http://www.thelivermorepgh.com', None, 'http://www.marriott.com/hotels/travel/pitel-springhill-suites-pittsburgh-bakery-square/', 'https://gelsbystormi.com', 'http://www.starbucks.com/store/9298/', 'http://www.magicwindow.ca', 'https://www.wellsfargo.com', None, 'https://www.marcosorder.com/?store=3582', None, 'http://yorktaps.ca', 'https://www.lasikmd.com/fr?utm_source=yelp&utm_medium=cpc&utm_campaign=calgary&utm_content=general-link&p_utc=YELP_paid', 'https://www.extraspace.com/storage/facilities/us/nevada/north_las_vegas/300030/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, None, 'http://www.fleetfeetcleveland.com', 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', None, None, 'https://local.lenscrafters.ca/on/thornhill/one-promenade-circle.html', None, "https://www.brueggers.com/?utm_source=yelp&utm_medium=homepage&utm_campaign=mayfield_heights&utm_term=Bruegger's%20Bagels%20Home%20Page", 'https://locations.wendys.com/united-states/al/madison/8814-hwy-20-w', None, 'https://www.bathdepot.ca/bath-depot-vaughan', 'http://www.lupitafernandezins.com?cmpid=d92d_blm_0006', 'http://www.aaatowing.ca', None, 'http://www.gilbertdentalcenter.com', 'http://fix8fitnesscafe.com/', 'http://www.jaroblue.com', 'http://fairwayindependentmc.com/', 'http://www.pittsburghwinery.com', 'https://www.wow1day.com/locations/house-painting-york?utm_campaign=yelp&utm_source=york&utm_medium=ubl', None, 'https://5starautocol.com', 'http://www.metrolinatire.com', None, None, 'http://palmerslawncare.net', None, None, None, 'http://www.tiffanymaidservice.com', 'http://www.reallysmooth.com', 'http://studio-kim.business.site', None, None, 'http://www.phohoa.com/', None, 'http://softmechanic.com', 'http://mastairaz.com', None, 'http://robertostacoshop.com', 'https://www.sonoraquest.com', 'http://www.dollar.com/Locations/gen.aspx?locationId=YTOC18', 'http://www.cpllabs.com/locations/patient-service-centers/cheyenne-psc.aspx', 'http://www.nguyenhuong.ca/menus.htm', 'http://www.fashionq1982.com', None, 'http://www.maddenbros.com', '1592182541', None, 'http://TresaApts.com', 'http://www.sanriva.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281379494&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, None, 'http://www.chevron.com', 'http://www.ruelo.com', 'http://burgerking.ca', None, None, 'https://www.uptowncleveland.com', None, 'http://www.dollartree.com/home.jsp', None, 'http://aerosportsparks.ca/brampton/', 'http://hummingbirddental.ca/', 'http://www.pghtours.com', '1592182590', 'http://www.amigotireslv.com', 'http://www.majesticmemorieslv.com/', 'http://www.eliteappliance.ca/', 'http://www.timhortons.com/', 'http://www.absolute-offroad.com', 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://www.deanshousestrongsville.com', 'http://www.sushiakaihana.com', None, None, 'http://www.sunocoinc.com', None, 'http://lvmpd.com/', 'http://lvdancesport.com', 'http://blasioleseatery.com', 'http://qualitycarstereoaz.com', 'http://www.sambucagrill.com', None, 'http://manhattandelimentor.com/', None, 'http://www.rockler.com/retail/stores/pa/pittsburgh-store', 'http://www.taxcomexicangrill.com', 'http://www.mobilespaelite.com/', 'https://www.walgreens.com/locator/walgreens-8500+w+cheyenne+ave-las+vegas-nv-89129/id=4197', 'http://www.bkreflex.com', 'http://Www.haringtonsplumbing.com', 'http://rjcrosby.com', None, 'http://www.coremotus.com/book-now', None, 'http://www.mathnasium.com/ocotillo', 'https://www.cleaneatz.com', None, 'http://www.gunsmithlasvegas.com', '1592182676', '1592182679', 'http://www.wachovia.com', 'http://www.secondcup.com', 'http://www.thelezzet.com', None, 'http://www.polishfestivalaz.org/', 'http://www.cmkpool.com', 'http://www.anniesgourmetitalian.info', None, 'http://www.cannabispatientcenter.com/', 'http://www.traderjoes.com', 'http://www.abcvalet.com', 'http://www.popshoppinautorepair.com', 'http://www.gnc.com', 'http://www.boldbeautyco.com', 'https://stores.thenorthface.com/WI/MADISON/USA24/', 'https://www.bannerhealth.com/locations/phoenix/banner-university-medical-center-internal-medicine', None, 'http://kimpovietnamese.com', 'http://familysbarbershop.com', 'http://www.olio.ca', None, 'http://www.dominos.com', 'http://onestopnutrition.com/', 'http://www.platinumcars.ca', 'http://www.fantasticfleamarket.com/', 'http://www.sapporopgh.com/', 'http://www.uniquedentalaz.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', None, None, 'http://www.theyogurtbaraz.com', 'http://www.papajohns.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/7499+West+Bethany+Home+Road+Corner+Of+75th-Glendale-AZ-85303/storeid=7872?cid=ps_ylp_2020', 'https://www.alohacleanersaz.com', 'https://www.mingsbubbletea.com', 'http://www.gokartslasvegas.com', 'https://www.brakemasters.com/location/5180-w-peoria-glendale-az/', '1592182778', None, 'http://www.cocochocolates.ca', 'http://www.showcaselandcare.com', None, 'http://www.bluewaveautospa.com', 'http://starfishandcoffeeshop.com', 'http://cohoots.com', None, 'http://shop.trisports.com/tempe', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282975370&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://www.nhmintviewobgyn.org/', None, 'http://www.stewartdetailing.com', None, 'http://bsalon11.com', 'http://www.northcoastlaser.com/', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', None, 'http://www.starbucks.com/store/9334/', 'http://kasianchiro.com', None, None, None, 'http://rtcsnv.com', None, 'http://monkeysushi.ca', '1592182939', 'https://www.bellagio.com/en/restaurants/sadelles.html', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', None, 'http://www.siegelsuites.com', 'http://www.bankofamerica.com', 'http://www.sloppykisseslv.com/', None, None, 'http://anthemhillsmusic.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.eliterepeatconsign.com/', 'https://www.zoup.com', 'http://thegymsportsbars.com', 'https://blackbeardiner.com/location/las-vegas-tropicana/', None, None, None, None, None, 'http://www.pachamamadc.com', 'http://www.econrads.com', '1592182988', None, 'https://www.jerseymikes.com/3128', 'http://www.indacutbarbershop.com/', 'http://www.pdubsbbq.com', 'http://www.bonaterrapgh.com', 'http://www.cessiespizza.com/', 'http://www.mark-taylor.com/arizona/ravenwood-heights/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.greatermatthewshabitat.org', None, 'http://www.modernchairrental.com', 'http://www.rhbarkleyhvac.com', None, None, 'http://www.riolasvegas.com/casinos/rio/restaurants-dining/hamadas-asiana-detail.html', 'http://accentricsalons.com', None, None, 'https://www.foodsocietyx.com', 'http://www.kay.com', 'https://www.eglintonsquare.ca', 'http://www.nicholascoffee.net', 'http://pinevilleplace.com', 'http://www.furry-pals.com', None, 'http://www.fantasticfades.ca', 'http://stratospherehotel.com/Food-Drink/Roxys-diner', 'http://www.villapizza.com', 'http://phoenixshoulderandknee.com/', '1592183053', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.sjnc.org/', '1592183060', None, 'http://fixautousa.com/las-vegas-north', None, 'http://www.lasvegas-cars.com', 'http://www.brimhallwellnesscenter.com', 'http://www.english.fgs2.ca/', None, None, 'https://locations.churchs.com/nc-charlotte-598', 'http://www.europeanautosalon.com', 'https://www.interdent.com/gentle-dental/locations/az/peoria/14155-n-83rd-ave-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.secondheartyoga.com', None, 'https://www.infinitiofbrampton.com', None, 'https://www.jlrichardscatering.com', 'https://madison.madhouseexperience.com', 'http://www.tempeuniversityinn.com', None, 'http://www.andersonaudiology.com', 'http://www.fionnmaccools.com', None, 'http://www.gelogisticsolutions.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.hairclub.com/locations/on/mississauga/hair-loss-clinic-228/?pub=loclisting&utm_source=yext&utm_medium=loclisting&utm_campaign=YX_228', 'http://www.hotyogatnt.com', 'https://locations.theupsstore.com/pa/mcmurray/4017-washington-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.cinemark.com/theatre-detail.aspx?node_id=97350', 'http://www.cuyahogalibrary.org/Branches/South-Euclid-Lyndhurst.aspx', 'http://www.wepoundemfishing.com', 'http://www.serviceking.com/locations/service-king-puritas?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://www.alsautorepair.mechanicnet.com', 'http://novabellasalon.mysalononline.com', 'http://www.cleatsinc.com/', 'https://phoenix.legacytraditional.org', 'https://beautyboxbyella.business.site', 'http://costcutters.com/salondetail/default.asp?salonid=62180', 'https://www.lafolieresto.ca', None, 'http://www.costco.com/WarehouseLocatorDetailsView?warehouseNumber=1121&storeId=10301&catalogId=10701', 'http://lakesidegrillestrella.com', 'http://www.barrecleveland.com/', 'http://www.cafemoka.us', 'http://www.midas.com/lasvegas/store.aspx?shopnum=1192&dmanum=480', 'http://www.verizonwireless.com/stores/arizona/tempe/tempe-marketplace-1088402/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://junskoreanlv.com/', 'http://www.smoothieking.com', 'http://restorecoldpressed.com', None, 'https://www.choicehotels.com/CN280?mc=blypypaf', 'http://www.earlyeducationpros.org', 'https://www.milansalonaz.com', 'http://www.tappsbar.com/', None, 'http://www.makisushi.ca', 'http://vibrantcare.com', None, 'http://www.marshallscanada.ca/en/directions.aspx?sid=741', 'http://www.thornhillskinclinic.com', 'http://www.union.lib.nc.us', '1592183182', 'http://buysellrent702.com', None, 'http://www.sugarshackaz.com', 'http://www.pizzahotwings.com', 'https://www.pizza73.com', 'http://allpages.com/', 'http://hairtiquedesignersinc.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.hunkmansion.com', 'http://www.nellos-pizza.com/', None, None, 'http://www.andrewleohairsalon.com', None, 'http://www.fullhousedesserts.ca', 'https://www.symphonywed.com', 'http://www.homesteadkennels.com', None, None, 'https://www.lasvegaseliteoffroad.com', None, None, None, 'http://www.dogworksmpg.com', 'http://www.rosarium.ca', 'http://www.piecesunimagined.com/', None, 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', None, 'http://www.groundsguys.com/madison', 'http://www.lovetowax.com', 'https://nailuxx-nail-salon.business.site', 'http://www.mooreinjurylaw.com', 'http://myfriendsrestaurant.com/site/', None, 'https://www.tillys.com/store?StoreID=0045', 'https://www.mosquito-authority.com/locations/scottsdale-az/', 'http://www.thesteammasters.com', 'https://www.thetreesurgeonpa.com', 'http://www.albertsgifts.com', None, None, 'https://www.usps.com/', 'http://www.kingorthodontics.com', None, None, 'http://tailsandscales.ca/', '1592183275', None, 'http://www.papajohns.com/', 'http://www.buonafurniture.ca', 'https://local.biglots.com/ky/henderson/190?zcp=pd_local_yelp', 'http://www.freshlysqueezed.ca', None, 'https://stores.nordstromrack.com/us/oh/westlake/30121-detroit-rd?utm_source=yelp&utm_medium=organic&utm_campaign=rack&utm_content=277&utm_channel=lcl_acq_p&sp_source=yelp&sp_campaign=rack', None, 'https://celebritytheatre.com', None, 'http://www.ryanhomes.com', 'http://www.bwmpetresort.com', 'http://www.diblasisbakery.com', None, None, 'http://clickserve.dartsearch.net/link/click?lid=43700044281380850&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.goldenspoon.com/', 'http://www.starrtreatments.com/', 'https://greatchoicechiro.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044281360228&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://cardenaslawgrouplv.com', 'http://www.coldstonecreamery.com/stores/20008', None, 'http://www.circlek.com/', 'http://www.vegasdiscountnutrition.net', 'https://islandpacificmarket.com/stores/listing/tropicana', 'http://www.madisonwindowtint.com', 'http://www.brueggers.com', None, 'http://giu.ca', None, None, 'http://www.paintingcontractorsohio.com', None, 'http://www.hmsmokeshop.com', 'http://www.sunsetboatrv.com', 'http://www.welderup.com', None, 'http://www.revolution-games.com', 'http://www.rocksidefamilydentalcare.com', 'http://www.accphx.com', 'https://locations.monro.com/pa/sewickley/209-ohio-river-blvd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'http://www.lumosarts.com', None, 'http://www.saswax.com', 'http://www.crutcherauto.net', 'http://www.puttersvegas.com', 'https://palmbeachtan.com/locations/AZ/Peoria-West-Thunderbird-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'http://clevelandhenna.com', None, None, 'http://www.sageandsandgrill.com', 'http://www.fillsgas.com', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', None, None, 'http://www.tonycordellphotography.com', '1592183388', None, 'http://www.cornerbarrestudio.com', None, 'http://www.bk.com', 'http://www.balletbarreworks.com', 'https://www.ghcscw.com/clinic/Hatchery%20Hill%20Clinic', 'https://www.la-z-boy.com', 'http://www.ecig-emporium.com', 'http://abcpoolservice.net', 'https://etobrestaurant.business.site', 'http://www.otherwideshoes.com', 'https://catchersfish.com', 'http://www.tigerkimstkd.com', 'https://www.take5oilchange.com/locations/oh/euclid-125/', None, 'http://www.esspa.net', 'http://www.allsewingmachinerepairs.com', 'https://www.sunrisepreschools.com/locations/broadway-mcclintock/?utm_source=yelp&utm_campaign=online_listing_tempe_274&utm_medium=referral&utm_term=business_url', None, 'http://planetzong.com/', 'https://www.choicehotels.com/pennsylvania/pittsburgh/comfort-inn-hotels/pa354/rates', 'http://www.starbucks.com/store/8054/', 'http://www.pillarcrowncourt.com', None, 'http://www.greenvalleyranchresort.com/dining/sushi-sake.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=GVR&utm_content=GVR-PROPERTIES&utm_campaign=GVR-YELP', 'http://CallAdvancedPro.com', 'https://www.bagelnash.ca', 'https://www.homedepot.com/l/Arrowhead-Ranch/AZ/Glendale/85308/475?cm_mmc=seo-yelp&', None, 'http://www.mattressfirm.com/', None, None, 'http://www.thepowerplant.org', '1592183453', 'http://www.donsbusbox.com', 'http://cheshirecataz.com/', 'http://www.dentistinstow.com', 'http://www.antiquecenterofstrabane.com', 'http://www.pointmanagementgroupllc.com', 'http://brightonevents.ca', 'http://www.autorepairaz.com', 'http://www.timelesshealthclinic.com', None, 'https://www.flyswoop.com', 'http://southpointcasino.com/dining/michaels-gourmet-room?cid=ypmic', None, None, None, None, 'http://www.bedfordnissan.com/', '1592183486', None, 'http://www.planetbouncepgh.com', None, None, None, 'http://www.jrlighting.com', 'http://monsoongroup.ca', '1592183503', 'http://www.familydollar.com', 'http://www.sachisalon.com', None, 'https://www.stancatos.com', 'http://www.substationii.com', None, 'http://www.ccdgp.com/', 'http://uhaul.com', 'http://wienerschnitzel.com/', 'https://www.wherefamiliesgrow.com', 'http://www.corksplayhousesquare.com', 'http://www.tempedogs.com', None, 'http://www.blowit.ca', None, 'http://www.thewokker.com', None, 'http://www.gianteagle.com', 'http://www.calgarybikram.com', 'http://www.fortresscreditpro.com/', 'http://www.honeymee.com', 'http://schnitzel.ca/', 'http://www.freshens.com', None, None, 'http://www.squashblossomaz.com', 'http://www.saharacenterlv.com/', None, 'http://www.unitedmayflower.com?Cpgn=Yelp', None, None, None, 'http://www.finewineandgoodspirits.com/webapp/wcs/stores/servlet/StoreCatalogDisplay?storeId=10051&catalogId=10051&langId=-1&utm_source=yelp&utm_medium=profile&utm_campaign=fwgsyelpfy17', 'http://ahwatukeehoa.com', None, 'https://www.scenariopgh.com', 'https://www.carowinds.com/things-to-do/dining', None, None, 'https://www.petsmart.com/stores/us/az/glendale-store0157.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://fastfix.com', 'http://www.starbucks.com/store/11823/', 'http://www.shapirocho.com', 'https://www.hungryhowies.com/store/hungry-howies-01824?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=1824&utm_content=Website_Link', None, 'http://www.metromoversgtanorth.ca', None, 'https://westernhonda.com', None, 'http://www.quiktrip.com', 'http://www.jeffspeakmanlv.com', 'http://www.fmentertainment.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=891&utm_content=bpas', 'https://www.gggflorist.net', None, None, None, 'http://www.birtsbistro.com', 'https://www.thepercantileandcreamery.com', 'http://www.geniusnetworkevents.com', 'https://www.esportafitness.com/Pages/clubhome.aspx?clubid=531', 'https://www.pinnaclemoderndentistry.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.glazecraze.ca', None, 'http://adfarm.mediaplex.com/ad/ck/24347-208272-18214-3', 'http://charlotteplumbing.com', 'https://stores.loft.com/outlet/us/nv/las-vegas/7400-las-vegas-blvd-south.html', 'https://www.wellsfargo.com', None, 'http://www.guess.com', '1592183651', 'http://www.therosehairstudio.com', 'http://www.cookmortgagegroup.com', None, 'http://www.LasVegasSegway.com', 'http://bennettautocare.mynapatools.com', None, None, None, 'http://www.kfc.ca/store/27-ruth-ave-brampton', None, 'http://www.lcbo.com', 'http://88noodlepapalasvegas.cafescentral.xyz', 'http://www.endurancerehab.com', 'http://www.rennsportire.ca', 'http://ladydianascakes.com/', 'https://locations.wendys.com/united-states/oh/cleveland/13939-euclid-ave.', None, 'http://www.MDA-Dentist.com/', 'https://ad.doubleclick.net/ddm/clk/300113982;127047679;f', None, 'http://www.toucheh.com', 'http://www.deathsdoorspirits.com', 'https://www.appliancepartscompany.com', 'http://www.toronto.ca/parks/island/', 'https://www.cinemark.com/arizona/cinemark-mesa-16', 'http://www.madisoninternationalspeedway.com', 'http://www.koolkatpgh.com', 'http://www.appliancesrepaircalgary.ca', None, None, None, 'http://www.reno4men.com/', None, 'http://scottsdale.house.hyatt.com/en/hotel/home.html?src=corp_yelp_businesslisting_phxxs_en_homepage_desktop&code=YB', 'http://www.servicecanada.gc.ca/tbsc-fsco/sc-dsp.jsp?lang=eng&rc=4802', 'http://ginassalonandwigs.com', None, 'http://phxnightclub.com/', '1592183735', None, 'http://www.heersmanagement.com/properties/property/del-mar-terrace-apartments', 'https://www.minutesuites.com', 'http://www.urban-baker.ca/', 'http://www.cactuslv.com', 'http://www.kandagreenhouse.com', 'http://englishhedgerow.com', 'http://www.universalcupcoffee.com', 'https://www.carmax.com/stores/7197?adcode=YLP7197&utm_campaign=LG_AFF&utm_source=LG_AFF_YLP&utm_medium=local&utm_content=shop', None, 'https://locations.dignityhealth.org/st-joseph-s-westgate-medical-center-glendale-az', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/1015+East+Ray+Road-Chandler-AZ-85225/storeid=7849?cid=ps_ylp_2020', None, None, 'http://yotapros.com/', 'https://www.giantmanhattanpizzaphoenix.com', None, None, 'http://www.masalakitchen.ca', 'http://www.zachmonroytraining.com/', None, 'http://www.livinggrace.net', 'http://homewoodsuites3.hilton.com/en/hotels/ontario/homewood-suites-by-hilton-toronto-markham-YYZHWHW/index.html?SEO_id=YELP-HW-YYZHWHW', 'https://stores.columbia.com/chandler-factory-store', 'http://www.wegotgamez1.ca', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', None, None, '1592183793', 'http://www.murphyappliance.ca', 'http://www.silkroadsushiandsteakhouse.com', 'http://www.mycdi.com/arizona/locations__services/', None, 'http://www.mypeacepreschool.com', 'https://www.inschoolwear.com', 'http://www.silverminesubs.com/', 'http://www.Arizonarvservice.com', 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'http://www.saharavegas.com/food/HouseofLords/', 'http://www.applianceservicecentre.ca', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.lesolson.com', 'http://www.phoenixpublicmarket.com/', None, None, None, None, 'http://www.theprophysiques.com/#home-top', 'http://www.eta-az.com', 'https://www.pizza73.com', None, None, 'http://radiocitypizza.com', 'http://www.yaharabay.com', None, None, 'http://www.ontariocourts.on.ca/scj/en', None, 'http://www.primroseestates.com', None, 'http://www.zonacaffe.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.jcsgrillhouse.ca/markham/', 'http://www.womensspecialtycare.com', None, 'http://www.ipetgrooming.com', None, 'http://www.perkykettle.com', None, 'http://www.tazzyandboo.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://alorestaurant.com/', None, 'http://Vegasonlinerealty.com', None, 'http://www.cynthiaschinese.com', 'https://locations.traderjoes.com/az/gilbert/258/', 'https://www.carlsjr.com/?utm_source=Yext&utm_medium=Visit%20Website&utm_campaign=Homepage', 'http://www.bestfloorcoatingsaz.com', 'http://www.scottsdalememorycare.com', 'http://www.evans-properties.com', 'http://www.lidlounge.com', 'https://www.supercuts.com/locations/az/surprise/albertsons-shopping-center-haircuts-82334.html', 'http://www.apnihavelly.com/', 'http://www.swisschalet.com', None, None, 'http://www.yangteashop.com', '1592183914', None, 'https://www.originaljoes.ca', None, None, 'http://www.BASISgoodyear.org', 'https://www.goodyear.com/en-US/tire-shop/Phoenix+AZ+85016-6808+US/000121764', 'https://www.pizzahut.ca/store-details/store-R42601/pizza-hut-Stouffville', None, 'http://www.foodlion.com', 'http://www.kegsteakhouse.com/en/locations/ON/toronto/esplanade-keg/', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', 'http://www.patelbros.com', None, 'http://blomedry.com/locations/blo-strongsville-ohio/', 'http://stylehousebeautybar.com', 'http://calgarysbestpubs.com/joyce/', None, 'http://www.artbuscoffee.com', None, 'http://www.galleriasm.com/branch/store/th', 'http://www.morcandirect.com', None, 'http://daluhairdressing.com', None, 'http://www.theencorequartet.com', 'http://www.unclebenspawnshop.com', 'https://www.olivegarden.com/locations/az/phoenix/metro-center/4410?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:phoenix-az-4410_pl:locurl_rd:1754', 'https://www.daveandbusters.com/locations/canada-oakville', 'https://www.westerndental.com/en-us/find-a-location/arizona/phoenix/13651-n-35th-ave', None, 'http://cargilleyecare.com', 'https://www.charmecochinchine.com', 'http://locations.michaels.com/nc/charlotte/5032/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://womensbookstore.com/', None, None, 'http://www.stellamiawestlake.com', 'http://cahairsalons.com', None, 'http://www.svahayogacenter.com', None, 'https://www.choicehotels.com/north-carolina/pineville/quality-inn-hotels/nc384/rates', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'https://www.theartofvapes.com', 'https://www.jetspizza.com/stores/illinois/champaign/512-s-neil-st?utm_source=Yelp-Ads&utm_medium=Yelp-Ads-SEO&utm_campaign=IL-008&utm_content=Website', 'http://www.cactuscrossfit.com', 'http://www.safeway.ca', 'http://justdogsgourmet.com', None, 'http://www.studio480thesalon.com/', None, 'https://southcharlotteservices.org', None, 'http://btnfurniturerepair.com/', 'http://www.bojangles.com', 'http://www.mississauga.ca/portal/discover/braebengolfcourse', 'http://exclusivecustomslasvegas.com', 'http://www.somersfurniture.com', 'https://no900.com', None, None, None, None, None, 'https://www.stateandmain.ca', 'https://www.ttc.ca/Subway/Stations/Pape/station.jsp', 'http://www.washwag.com', 'http://www.ritasfranchises.com/ArcadiaTowneCenter', 'http://www.loova.com', 'http://www.xpandrealty.com', '1592184055', 'http://www.petagreemobilespa.com/', 'https://www.simplyravishingsalon.com', 'http://www.dreamtherapies.com/', None, 'http://www.perrinofurniture.com', 'https://www.guaranteedrate.com/loan-expert/joecordone', 'http://www.strudelteig.com', '1592184073', 'http://www.bremec.com/BremecOnTheHeights.htm', 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.arizonaroofingcompany.com/', None, 'http://www.anthropologie.com/', '1592184083', 'http://www.firstcu.coop', 'http://www.gristle.catering', 'http://www.hartswastedspace.com', 'https://www.chilis.com', 'http://www.elementalplumbing.com', 'http://www.northmountaingrille.com', None, 'http://www.meridiancu.ca', 'http://www.elitemoversofcleveland.com', 'http://www.jackalopejacks.com/', None, 'http://www.avenueliving.ca', None, 'https://www.hudsonsrestaurant.com', 'http://www.yojuicylife.com', 'http://bloorwestcosmetics.ca/', None, 'https://locations.nekterjuicebar.com/ll/US/AZ/Phoenix/4340-Indian-School-Rd_*-Ste_-19?utm_source=yelp&utm_medium=link&utm_campaign=Indian-School&utm_content=URL', 'http://www.vintagethai.ca', None, '1592184122', 'http://www.artistsuncorkd.com', None, 'http://www.tiedemannglobe.com', 'http://saveamuttkennel.info', None, 'http://www.bedsidemanor.com/', 'http://www.silversevenscasino.com/', None, 'http://www.lobbyrestaurant.com/', None, 'http://lindeyslakehouse.com', None, 'https://www.ubreakifix.com/ca/locations/thornhill', 'http://kwikkleaning.webs.com/', 'http://www.gemoftheearth.com', 'http://www.charlottelaserdentist.com', None, None, None, 'http://www.exquisitenailsandspa.ca/', None, 'http://www.jfcsaz.org/site/c.ajIQK6NMLfJ0E/b.6211177/k.2AE8/Contact_Us.htm', 'https://tabletennisandmore.com/phx/tabletennisandmore/', None, 'http://www.7-eleven.com/?yelp=22886', None, None, 'http://www.bodytherapyaz.com', None, 'http://www.westvalleypetsitting.com', None, 'http://www.capitano.ca', 'http://www.renusskincare.com', 'http://scorpionridge.com', 'http://www.cfcgiftcard.com', 'http://www.sandovalkarate.net', 'https://abrazomedicalgroup.com/amg-parkway/robert-l-bierman-md/', 'http://www.lifeisbeautifulsalon.com', 'http://www.upnsmokepitbbq.com', 'http://www.kensingtonmakeup.com', 'http://www.saryocafe.com', None, 'https://www.interdent.com/gentle-dental/locations/az/phoenix/4910-e-chandler-blvd-dentist-office?utm_source=organic&utm_medium=yext', None, 'http://www.reposesalonandspa.net', None, None, 'http://www.xingfutang.ca', None, None, 'http://www.challengerbasic.com', 'http://www.farrarjewelers.com/', 'http://www.oakandvine.ca', None, None, 'http://northernhillsdental.com', 'http://www.madvapesindianland.com', 'http://4sonsstores.com/29', None, 'http://www.cashamerica.com/SUPERPAWN-stores/NV/LASVEGAS/LV02', 'https://www.ubreakifix.com/ca/locations/avenueroad', None, 'https://www.hamiddonair.com', 'https://only-inspections.com', 'http://www.restauranttrentina.com/', None, 'https://www.petsuppliesplus.com/Store/SC/Fort-Mill/Fort-Mill/4189', None, 'http://www.skinnywimpmoving.com', 'http://www.auntieannes.com', None, 'http://www.toshoknifearts.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216608&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://wisconsinrepair.com', None, 'http://www.valleysolaraz.com', 'https://www.walgreens.com/locator/walgreens-1159+e+southern+ave-mesa-az-85204/id=3670', 'https://www.cineplex.com/Theatre/cineplex-cinemas-winston-churchill', 'http://www.peaksathleticclub.com', 'https://www.servproscottsdale.com', 'https://www.ventitobakery.com', 'http://www.northscottsdalehyundai.com/', None, 'http://www.metrofireaz.com', None, 'http://www.wingstop.com/', 'http://www.sallybeauty.com', None, None, 'http://hrhc.lv/PinkTaco', 'http://www.addisononerinmills.com/', None, 'https://local.fedex.com/nv/las-vegas/office-1441/', 'http://www.heartpathacupuncturemadison.com/', '1592184312', 'http://www.carolinaexpressclinic.com/', 'http://www.insuranceinwhiteoak.com?cmpid=ts6n_blm_0006', 'http://www.apachewellscountryclub.com', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/mississauga-2191-dundas-street-e.aspx', None, 'http://www.bathandbodyworks.com', None, 'http://www.bestbuy.com', 'https://iisnv.com', 'https://www.topmasterlocksmith.com', 'http://www.lowes.ca', 'http://www.primrosehuntersville.com?utm_source=yelp&utm_medium=maplistings&utm_campaign=localmaps', 'https://stores.jcpenney.com/wi/madison/clothing-stores-madison-wi-0891.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-0891', 'http://www.mcdonalds.com', 'https://1stpetvet.com/locations/north-valley-az/', None, 'http://www.rxboilerroom.com', None, 'http://www.brakemasters.com', 'http://www.familydollar.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://liasgardenbanquethall.com', 'https://www.menswearhouse.com/store-locator/2505?utm_source=yelp&utm_medium=listing&utm_content=2505&utm_campaign=AZ', 'http://freshmexican.wix.com/hermanos', 'http://www.miramaestudio.com/#!services/c166e', None, None, 'http://www.harrisgrill.com', 'http://www.tiffany.ca/', 'http://www.saloonofmtlebanon.com', 'http://priorityonefit.com', None, 'http://www.miseryinktattoobodypiercing.com/', 'http://hongto.weebly.com/', 'https://solsouthwestkitchen.com/#locations', 'http://nexusrehabspine.com/phone/index.html', 'http://www.vivaladivalv.com', 'http://www.eastcoastweapons.com/', 'http://www.arizonaglasspros.com', None, 'https://www.fishertools.com', None, 'http://panzapiena.ca', None, 'http://www.sunocoinc.com', 'http://redwagondiner.com/', None, 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', '1592184420', None, 'http://local.firestonecompleteautocare.com/arizona/peoria/10661-n-84th-ave/?lw_cmp=IYP_YPC_MLP_11932', 'http://www.starbucks.com', 'http://www.thenailroomlv.com', 'http://www.nunziospizzeria.com', None, 'https://shopmarketandco.com/merchant/seed-to-sausage/', 'http://www.clarkcountynv.gov/Depts/parks/Services/pages/picnic-area-reservations.aspx', 'http://www.azstudentmovers.com', 'https://www.itcu.org/about/locations/green-valley', 'http://www.runningroom.com/hm/inside.php?id=2332', None, 'http://www.pareagyros.com', 'http://paladinautomotivelasvegas.com', 'http://automaticgaragedoorcompany.com', 'http://www.azcentral.com', 'http://www.gotourscanada.com', 'http://commercialcenterdistrict.com', 'https://thesaguaro.com/scottsdale/#hotel-spa', 'http://www.einsteinbros.com', 'https://www.desertstateinspections.com', 'http://local.firestonecompleteautocare.com/north-carolina/charlotte/5340-e-independence-blvd/?lw_cmp=IYP_YPC_MLP_10790', 'http://www.clarkcountynv.gov/Depts/parks/Pages/clark-county-museum.aspx', 'http://www.goodlifefitness.com', 'http://www.eSMIL.com', None, 'https://moxies.com/restaurant-locations/ontario/richmond-hill-beaver-creek', 'https://twomaidsgilbert.com', None, 'https://my.clevelandclinic.org/locations_directions/regional-locations/avon-lake-fhc', None, None, 'https://www.redlobster.ca/locations/list/on/toronto/20-dundas-street-west', 'http://www.dvfmaz.net', None, 'http://thevaporloft.com/', 'http://www.dineoncampus.com/UNCCharlotte/', 'http://www.celebrationsbarandgrill.com', 'http://heyrestaurant.tumblr.com/', 'http://www.dunkindonuts.com', None, None, None, None, 'http://www.clarkcountynv.gov/depts/parks/Pages/parkslocator.aspx', 'http://www.dillonsontopofcentral.com/', 'http://www.omegahomeimprovements.com', 'http://talleyproperties.com', None, 'http://www.chandelier-hair.com', 'http://www.serenityflorals.com', 'http://hbsalonnc.com', 'https://www.crawfordsautoservice.com', 'http://www.newsons.ca', 'https://www.tempevistabyavanti.com', None, 'http://www.leons.ca/', 'https://www.giuseppeson28th.com', 'https://diamondlaw.ca/toronto', None, None, 'https://www.greulichs.com', None, None, 'http://www.scottsdaleskininstitute.com/', 'https://germancarspecialist.com', 'https://locations.wendys.com/united-states/pa/swissvale/1703-s.-braddock-ave', 'http://www.greekvillagegrille.com/', 'http://www.neptunehairstyling.com', 'http://www.dollartree.com', None, 'http://www.trucksonlysales.com', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Calgary-AB-T2Z4M8/058072/', 'http://www.karenshairdesigns.com/', 'http://mothernaturesdiapers.com/', 'http://www.arizdental.com', 'http://www.johnnysonfulton.com', 'https://agents.allstate.com/adam-brown-las-vegas-nv-14515251.html', 'http://www.lasvegasdiscountbeds.com', 'http://www.cactuspools.com/', 'http://www.skytecsecurity.com/', 'http://paintingcontractorglendale.com', 'http://www.carters.com/home?id=carters&cm_mmc=Retail-_-Carters-_-Yelp-_-April', None, 'http://azempiredoors.com', 'https://www.millers.com', None, 'https://thegoatbarandgrill.com', None, 'https://davids-diner.business.site', 'http://www.clevelandart.org', None, 'http://theclevelandarcade.com/', 'https://locations.jackinthebox.com/us/az/chandler/900-n-cooper-rd', 'http://www.gap.com', 'http://www.janetscustomsewing.com', '1592184613', 'http://xtremecleanmobile.com', 'http://sfsourdougheatery.com/', 'http://www.randitas.com', 'http://steliotesdentalspa.com/', None, 'http://www.sushisushi.ca/', None, 'http://www.duzz.ca', None, None, 'https://arizona.weidner.com/apartments/az/phoenix/skyline-lofts-0/?rccustomid=Mjc%3d-uldpF8AWDTo%3d', 'https://dealer.sprint.com/experts-choice', 'http://www.aztecatowingarizona.com', 'http://mannysdiscount.com', None, None, 'http://www.sterlingsteelecreek.com', 'https://www.nofrills.ca/store-locator/Dennis%27+nofrills+%28Erin+Mills+Parkway%29/0700?storeId=0700', 'http://www.libertyfordbrunswick.com/', 'http://pro-techtransmission.com', 'http://www.cozumelrestaurante.com', 'https://www.choicehotels.com/pennsylvania/pittsburgh/quality-inn-hotels/pa476?source=pmfyelp&pmf=yelp', 'http://www.scottmillerdds.com/', 'https://www.escapecampervans.com/locations/las-vegas-nevada/', 'http://automotiverepairphoenix.com', None, 'http://www.bathandbodyworks.com', None, None, None, 'http://www.a1qualitycare.com/', 'http://madisongaragedoorservices.com', 'http://local.firestonecompleteautocare.com/arizona/mesa/1553-s-crismon-rd/?lw_cmp=IYP_YPC_MLP_784290', 'http://petstellthetruth.com/', 'https://www.circlek.com/store-locator/us/chandler/1405-n-alma-school-rd/2705973', 'https://www.dentistryatgreenway.com', 'http://duckyschampaign.com', 'http://www.paddyspourhouse.com', None, 'http://www.saffrontakeout.ca', 'http://www.overflowcafe.com', 'https://www.bankofamerica.com', 'http://msquarecoffeeco.com/', 'http://Clearqualityautoglass.com', 'http://www.nicolebodyworks.com', 'https://www.homedepot.com/l/Avon-Vail/CO/Avon/81620/1525?cm_mmc=seo-yelp&', '1592184707', None, None, 'http://99only.com/store/Phoenix---12th-St./', 'http://www.oasispediatrics.com', 'http://www.krispykreme.com', 'http://www.calgaryscrapautoremoval.com', None, None, None, 'https://jamesgoodnow.com', 'http://www.nps.gov/lake/index.htm', 'http://www.aiellospizzeriallc.com', None, 'https://local.fedex.com/az/glendale/office-1471/', 'http://pecoslawgroup.com', 'https://www.handlebarj.com', 'http://www.courtoneaz.com/', 'http://www.desertrad.com', 'http://trubliss.com', 'http://hotduckaz.com', 'http://www.starbucks.com/store/14887/', 'https://glassdoctor.com/henderson', 'http://www.momdocwfw.com/scottsdale', 'https://www.calforex.com/en/locations/foreign-exchange-vaughan-on-vaughan-mills/', 'http://www.truwest.org', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.designateddriversinc.com', None, 'https://f45training.com/southwestlasvegas/home', None, None, 'http://bellavitaitaliangrille.com/', None, 'http://www.mark-taylor.com/arizona/san-lagos/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.azhomedefense.com', '1592184786', None, 'http://www.hooters.com', 'http://www.atlccleaningcompanyllc.com', 'http://christinanailboutique.com', None, None, 'http://tamidairiki.md.com/', 'http://www.azallergy.com', 'http://www.DymeBoxing.com', None, 'http://www.toplimolasvegas.com', 'http://livingwellhomes.com/apartments/details/brookfield_homes', 'http://www.dermsolutionsaz.com/', 'https://wickenburg-alternative-medicine.business.site', 'http://www.lapetite.com/your-local-school/north-las-vegas-nv-7306', 'http://lasvegasstripweddings.com/', None, None, 'http://www.newamericanagent.com/steveschauer', 'http://www.ocean-prime.com/locations-menus/phoenix', None, 'http://tajindiancuisineaz.com', 'http://www.adidas.com/us/storefinder', None, '1592184835', 'http://ranchosecurity.com/', None, 'http://www.foodlion.com', 'http://www.thebeadery.ca', 'http://www.othermothersaz.com', None, 'http://www.esmokercanada.com', None, 'http://www.carmodysgrille.com', None, 'http://littlemacau.com/', 'http://AnimalCareClinicInc.com', None, None, None, 'https://www.hilton.com/en/hotels/phxruru-tru-gilbert/?SEO_id=YELP-RU-PHXRURU', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.tocasierraspa.com', 'http://www.buffalowildwings.com/?utm_source=yelp&utm_medium=yelp_profile&utm_campaign=yelp_locations', None, 'http://www.fortmcdowellcasino.com/home.php', 'http://www.pridebeautystudio.com', 'http://www.restaurantrouby.ca', 'http://sawasdeethaitogokitchen.com', 'https://mountainsidefitness.com/locations/carefree/', 'http://www.copps.com/', 'http://locations.saksoff5th.com/en/phoenix', 'http://www.canadiantire.ca/en/store-locator/ab/calgary-south-ab.store.html', 'http://www.hansonwater.com', 'http://www.gussdiner.com/', None, 'http://ladoniacafe.com/', '1592184905', None, None, 'https://www.dynacare.ca/specialpages/secondarynav/find-a-location/toronto-center-(1).aspx', 'https://www.floristinrockyriveroh.com/?srccode=yelp_track', 'http://www.menasgrill.com', 'https://gohoneyhut.com', 'https://footsolutions.com/phoenix/', None, None, None, 'http://www.minervaindiancuisine.com/', 'http://savoypgh.com/', None, 'http://www.peoples-gas.com', 'http://www.shopjustice.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'http://www.bollywood-bites.com', None, 'http://myazlawyers.com/', 'http://heartschoices.com/calgary-farmers-market/', None, 'http://www.dicey.biz', 'http://crazyburrito.ca', 'http://www.Montblanc.com', '1592184965', 'http://www.beadworldinc.com', 'http://www.lvcharleston.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, None, None, None, None, 'http://www.muchoburrito.com', 'http://www.pitaland.ca', None, None, None, 'http://www.rideabike.com', 'http://www.shicklaw.com', 'http://www.revivestainlesssteel.com', 'http://www.thebespokeman.com', 'http://www.cavecreeklock.com', 'http://www.chestermerelanding.com', 'https://www.canyonstateauto.com', 'http://6ixbar.com', 'https://www.regmovies.com/theaters/ua-showcase-theatre-8/C00542780062', None, None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7784&localechange=1', 'https://www.aldoshoes.com/us/en_US/store-locator/store/2103', 'http://www.kingsrestaurant.net', None, None, None, 'http://www.sarahhorne.org', None, 'https://www.rentvegas.org', 'https://cocktailantabli.com', 'http://dosgringosaz.com', 'https://www.regus.com/?utm_medium=portal&utm_source=YelpNA', None, None, None, 'https://www.fsequence.photography', 'http://www.petgroominglv.com', None, 'http://www.mississauga.ca/portal/residents/mississaugavalleylibrary', None, 'https://oakarizona.com', 'https://www.nightowlcontractors.com', None, 'http://robertostacoshop.com', 'http://gravady.com', 'http://www.humblepieusa.com/', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=14057&localechange=1', None, 'http://www.farwellpools.com', 'http://www.bin110.com', 'http://www.crocs.com', 'http://tricitycardiology.com', 'http://www.larkspurcatclinic.com/', 'https://www.sunrisechildrenshospital.com', None, 'http://www.theroofdoctorlv.com', None, 'http://www.altacamelback.com', 'https://locations.timhortons.com/ca/on/oakville/494-dundas-st-w.html', 'https://www.currys.com', 'http://perfecthomefurniture.com', None, 'https://www.abraauto.com/abra-auto-location/1058-concord-nc', 'http://www.patricksimonedds.com', 'http://www.lvendocrinology.com', 'http://www.chandlerapthomes.com', 'http://www.desirableskinaz.com', 'http://www.flooringsurfacesinc.com', 'http://www.travelgolfcenter.com', None, 'https://www.jetblue.com', 'https://www.bahamabreeze.com/locations/nv/las-vegas/las-vegas/3020?cmpid=br:bb_ag:ie_ch:dry_ca:BBQ121LOCURL_dt:20200605_sn:yelp_gt:las-vegas-nv-3020_pl:locurl_rd:1013', 'http://www.weknowurban.com/Phoenix/', 'http://www.thorncliffebowlerama.com/', 'http://www.queenspectacle.com/', 'http://www.linenchest.com', 'https://www.redrobin.com', None, None, '1592185140', 'http://lemontblancbanquets.ca', 'http://nolimitska.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.highlandfarms.ca', 'http://www.firkinpubs.com/thefrogandfirkin/', None, 'http://www.papamurphys.com/', None, None, 'http://www.dacordplumbing.com', 'https://www.championwindow.com/Cleveland/?lpc=UU-OD-Cleveland-Yelp&source=ol-yel01&utm_source=yelp&utm_medium=local&utm_campaign=Cleveland', 'http://bundtz.com', 'https://caringhandsvetlv.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://clearchoicetechnical.com/service-locations/las-vegas', 'http://www.devinetouchmassage.com', 'http://www.nirvanahome.ca/', 'http://www.robertgodridgephotography.com/', 'https://www.maidsinblue.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.enblumcatering.com', 'https://atriumhealth.org/locations/detail/carolinas-medical-center-mercy', 'http://www.gilbertazpediatricdentist.com/', 'http://www.screwielewies.com/', '1592185190', 'http://www.sapporolv.com', 'http://www.galaxyhobby.ca/', 'https://azpyramidservices.binbooker.com', None, None, None, 'https://www.modernround.com/locations-peoria.html', 'http://livingwelltakeout.net/', 'http://www.balletossington.com/', None, '1592185212', 'https://agents.farmers.com/az/chandler/joe-baselice?SourceID=AMPALFYEAG&utm_medium=Local&utm_source=Yelp', None, 'https://www.get-go.com', 'https://www.ulta.com/stores/glendale-wi-646', 'https://www.cox.com/local/residential/stores/az/gilbert/2150-east-williams-field-rd?sc_id=dp_z_yext_z_store_19Q2?sc_id=dp_z_yelp_z_store_19Q36', 'https://www.olivegarden.com/locations/az/phoenix/metro-center/4410?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:phoenix-az-4410_pl:locurl_rd:1754', None, 'http://www.passionfordesserts.ca', 'https://www.aqua-tots.com/chandler/', 'https://www.handy.com/yelp50cc?utm_source=yelp&utm_medium=CPC&utm_campaign=TOR-Handy-Yelp', 'http://www.xcash.ca', None, 'http://www.mysweetbasil.com', 'https://www.sassoon-academy.com/en/academy/north-america/toronto', None, None, 'http://www.toytownplaycenter.com', 'https://my.clevelandclinic.org/locations_directions/Regional-Locations/twinsburg-fhsc', None, 'http://www.tabbyandjacks.com', None, None, 'http://enhancedcare.ca', None, 'https://www.gianteagle.com/Stores/Store/?storeId=224', None, 'http://www.kay.com', None, 'http://www.jimshorkeyford.com/?ibp-adgroup=YX_Target', None, None, None, 'https://www.granitetransformations.com/location/granite-transformations-of-northeast-ohio/?utm_source=Yelp&utm_campaign=2018', 'http://www.greentreefootandankle.com', 'https://medmen.com/stores/las-vegas-the-strip-paradise-and-harmon/', None, None, None, None, None, 'http://www.paradisehalls.com', 'http://www.jamrockcafe.com', None, 'http://www.ocadu.ca/', 'http://www.bathandbodyworks.com', 'http://www.hollywoodtans.com', 'http://gehomeservicesllc.com', 'http://eosfitness.com/location/peoria?utm_campaign=peoria&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', 'https://www.firehousesubs.ca', 'https://nationwidevision.com/locations', 'http://www.doubledspizzas.com', 'http://www.waxandlash.ca', 'https://www.tidesonthomas.com', 'http://l.macys.com/superstition-springs-center-in-mesa-az?cm_mmc=Yelp_Stores-_-Mesa-_-n-_-459&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Mesa_459&m_ac=yelp_stores&m_ag=n', 'http://fiveguys.com/', None, 'http://www.fastlanecoatings.com', None, None, None, None, 'http://peignedancestudios.com', None, 'http://www.scottsdalesilveradogolfclub.com/', None, 'http://www.fithcc.com', 'https://tattoocorner.business.site', None, 'http://www.fransrestaurant.com', 'http://www.thelittleclinic.com', None, 'http://www.copperstatehandymanservices.com', None, 'http://www.soniasbridalstudio.com', 'http://sollidcabinetry.com', 'http://www.dukephototempeaz.com', None, 'http://www.city.cleveland.oh.us/CityofCleveland/Home/Government/', '1592185371', 'http://www.saukpointvet.com', 'https://www.duckdonuts.com/location/orange-village-oh-2/', 'https://www.starlitebbq.com', None, None, 'http://www.tartucollege.ca/', 'http://sanctuary-salon-spa.com', None, 'http://www.swignsweets.com', 'http://englishbayfish.ca', 'http://www.riderta.com/facilities/airport', None, 'http://www.arbys.com/', '1592185397', 'http://northmesaauto.com', None, 'https://www.buffalowildwings.com/en/food/?utm_source=Yelp&utm_medium=organic&utm_campaign=yelp', 'https://www.phillipslaw.com/phoenix-arizona-personal-injury-lawyers', 'http://www.momdocwfw.com/estrella', 'https://thelearningexperience.com/preschoolsuccess?utm_source=Yelp&utm_medium=Referral&utm_campaign=Sponsored+Business+Listings', 'http://www.harveyspaint.com', 'https://www.screensunlimited.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.bombayexpresstoronto.com/', None, 'http://www.dominos.com', 'http://www.beautyavenue.us', 'http://www.thethirdestimate.com/', None, None, 'http://1stchoicemechanicalaz.com', 'https://redrock.sclv.com/Dining/Grand-Cafe?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.glockmeister.com', 'http://greenjadechampaign.com', None, '1592185448', None, 'https://escapetheroom.com/phoenix/', None, 'http://www.atthebarns.org/', 'http://www.thebagelcafelv.com/', None, 'http://www.spicypickle.com/restaurants/arizona.html', None, None, 'http://www.dollarama.com', 'http://www.aaaactiondoors.com', None, None, None, 'http://www.lobtoronto.com', 'http://www.happyspizza.com', 'https://locations.comerica.com/location/75th-thunderbird', None, 'http://servitaxlv.com', 'http://www.azdot.gov/mvd', 'http://www.perinatal.com', 'https://www.imagedentallasvegas.com/?utm_source=yelp&utm_medium=link&utm_campaign=yelp', 'http://www.pghoptical.com', None, None, 'https://www.mckenziesmidtown.com', 'http://www.redsearestaurant.net', 'http://www.mallorcarestaurant.com', 'http://broadviewbeauty.ca', 'https://www.homecitybnb.com', 'https://local.fedex.com/oh/bedford-heights/LNNA/', 'http://www.guschaletrestaurant.com', None, 'http://www.tinyboxvapeshop.com', 'http://www.barrettfinancial.com', '1592185518', None, 'http://www.delanolasvegas.com/en/nightlife/skyfall-lounge.html', None, '1592185526', None, None, 'http://www.openarmspreschool.ca', 'https://www.jerseymikes.com/9004', 'https://locations.sonicdrivein.com/az/mesa/3033-e-mckellips-road.html', 'http://www.phoenixfamilymedical.com/', 'http://www.capitaldrip.com', None, None, 'http://www.handelsicecream.com', None, 'http://www.kaleidoscope-living.com', '1592185552', 'http://www.head2toechiro.com', 'http://www.eastvalleyfloors.com', 'http://www.scrapbookbarngilbert.com', None, 'http://www.nextcare.com/locations/az/peoria-glendale/?utm_source=Yelp&utm_medium=Local&utm_campaign=peoria_glendale', 'http://www.relaxologywellness.com', 'https://theoaksevents.com', 'http://www.imsiamlasvegas.com', None, 'https://www.restaurantohsushi.com', 'http://www.troplv.com/meetings-and-events/havana-room', None, 'http://www.lvms.com/bullring', 'http://www.antoniospizza.net', 'http://arbortrimming.com', None, 'https://www.venetian.com/towers/the-palazzo.html?utm_source=yelp&utm_medium=partner&utm_campaign=businesslisting', None, None, 'http://www.rajdhanisweets.ca', 'http://www.cashmanphoto.com', None, None, 'https://agent.amfam.com/nv/north-las-vegas/colleen-drinnon/', 'http://www.grandtouringautos.com/', 'https://locations.wendys.com/united-states/az/laveen/3520-w-baseline-road', 'http://www.fuzesalon.ca', 'http://gerchickrealestate.com/', 'https://greenvalleyranch.sclv.com/?utm_source=YELP&utm_medium=SOCIAL&utm_term=GVR&utm_content=GVR-PROPERTIES&utm_campaign=GVR-YELP', 'http://hamptoninn3.hilton.com/en/hotels/ontario/hampton-inn-by-hilton-toronto-airport-corporate-centre-YTOSOHX/index.html?SEO_id=YELP-HP-YTOSOHX', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', None, 'http://www.everythinginsight.net/our-practice.html', None, None, None, None, None, 'http://www.petco.com', 'http://www.willietys.com/', 'http://www.sidebarphoenix.com', None, None, 'http://www.pandahobby.store', 'https://dealer.sprint.com/experts-choice', 'http://illinishuttle.com', None, 'http://www.instylenail.ca/', 'http://www.mcdonalds.com', 'http://www.clhairartstudio.com', None, None, None, 'http://www.garciaswm.com/', None, 'https://locations.einsteinbros.com/us/az/surprise/13746-w-bell-rd', 'http://www.michaelsbridalgalleria.com', 'http://www.penn-station.com', 'http://www.prmvineyards.com', 'http://Mindbodysoles.net', 'http://EvansLasVegas.com', None, None, None, 'http://www.carolinavaluevillage.com', 'https://locations.whataburger.com/az/scottsdale/2955-n-hayden-rd.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', 'http://www.coolclubs.com', 'http://Azkickbacktours.com', 'https://www.phoenix.gov/parks/sports/complexes/desert-west', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.trilliumweightloss.com', 'http://www.runningwiththebullsusa.com', 'http://saporebyzafferano.ca/', None, None, 'http://www.thehkan.com', 'http://www.hayleylynnedoeshair.com', None, 'http://www.cotswoldfarmersmarket.com', 'http://www.kaleidoscopejuice.com/', 'http://www.harrysgrilleandtavern.com', None, 'http://local.biglots.com/az/gilbert/1913?zcp=pd_local_yelp', 'http://www.scottsdaleobgyns.com/russellBartelsMD.html', 'http://www.yourcarinsiders.com', 'https://www.supercuts.com/locations/pa/pittsburgh/shadyside-plaza-s-highland-haircuts-8953.html', '1592185734', None, None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.yknotparty.com', None, None, 'http://local.firestonecompleteautocare.com/ohio/north-olmsted/4580-great-northern-blvd/?lw_cmp=IYP_YPC_MLP_14796', 'https://www.saksfifthavenue.com/locations/s/sherwaygardens', None, None, 'http://www.vintagehomecharlotte.com', 'http://Www.aglowbeautybarlv.com', 'http://www.carolinaherrera.com', None, 'http://www.activegreenross.com', None, None, 'https://locations.whataburger.com/az/mesa/1947-w-broadway-rd.html/?utm_source=yextpages&utm_medium=locallistings&utm_campaign=yextpages', None, None, 'http://locopatron.com/', 'http://livewellmassage.vpweb.com', None, 'http://www.mammaspizza.com', 'http://www.victoiredayspa.ca', 'http://www.outback.com/locations/nv/las-vegas-craig', 'http://bandnautosalesllc.weebly.com', 'http://us.shop.ecco.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://firenzastone.com/', None, None, 'http://auxiliarycrossfit.com', 'http://www.capitolpetroleumllc.com/site/', 'http://www.pogllc.com', None, None, 'http://www.legendscafelv.com', 'http://www.sweetlifegelateria.com', 'http://www.clutchlandscaping.com', 'https://www.lesinsulaires.ca', 'https://www.circlek.com/store-locator/us/scottsdale/20721-n-scottsdale-rd/2705915', 'http://mine-sushi.com/', '1592185823', 'http://www.tsingtaomesaaz.com', 'http://www.Friendly-Wireless.com', 'http://www.bmvbooks.com/', 'http://www.smoochiepoochiedoggrooming.com', 'http://www.LaurenParis.com', 'https://www.wyndhamgardencalgaryairport.ca', None, 'https://www.calgarycoop.com/stores/shawnessy/', None, None, 'http://bosadonutsaz.com', 'https://www.ganleylincolnohio.com', 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/brampton-7688-hurontario-street.aspx?postalcode=L7A+3R9&storeid=66', None, 'http://www.thestratford.org/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', None, 'http://www.eddiebauer.com', 'http://www.tempritelv.com', None, 'https://www.saksfifthavenue.com/locations/s/phoenix', 'http://www.carolinavet.com/locations/matthews-nc/', 'http://aestheticbodycontouring.net', None, 'http://www.ganleysubaru.com', 'https://vbarbershop.com/location/chandler-fulton-ranch/', 'http://www.bellanailshop.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://hashtaggallery.com', 'https://locations.theupsstore.com/nc/matthews/2217-matthews-township-pkwy?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', None, 'https://www.uhaul.com/Locations/Truck-Rentals-near-Henderson-NV-89011/807058/', 'http://www.heislersmarket.com', '1592185901', None, 'https://www.esso.ca', 'http://www.hogwildpitbbq.com', None, None, '1592185915', 'https://www.kohls.com/stores/az/glendale-652.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.indiasflame.com', 'http://www.brightoncollisioncenter.com/', None, 'http://workoutquest.com', 'http://www.eagerbeaverplumbing.com', 'http://allens-pool-catering.business.site', '1592185934', 'http://www.ostlerfamilydental.com', 'https://chutneyb.com', 'http://www.ae.com', None, 'http://vspconsignment.com', 'https://www.zipscarwash.com/location/rock-hill-sc/', 'http://www.teresaspizza.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.morphebrushes.com', None, 'http://schwans.com', 'http://lovekimnailsspa.wix.com/home', None, 'http://www.earthangelsholistic.com', None, None, 'http://8thwonderstudio.com', 'http://www.bowtiepizza.com', None, 'http://www.eggsmart.ca', None, None, 'http://www.chapters.indigo.ca/home/storelocator/storeDetails/929/', 'http://www.donvalleyvw.net', 'https://druxys.com/location/2-st-clair-ave-colonia-place/', 'http://www.aemediaproduction.com', 'http://www.wingmachine.com', 'http://www.lvmis.com', None, 'http://www.vegaspubcrawler.com', None, 'http://www.jeromesalon.com', 'http://www.transformerstation.org/', 'https://lasvegas.adamevestores.com', 'http://www.dvtowing.com', None, None, 'http://Longevityinfitnessexcellence.com', 'http://www.smilebeautifuldentistry.com', 'http://www.marriott.com/hotels/travel/yyzap-courtyard-toronto-airport', 'http://www.urbanbloomcurls.com', 'https://www.willowpark.net', None, 'http://local.biglots.com/az/phoenix/4085', None, None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://rogersandhollands.com/east-towne-mall', 'https://starliterestaurant.ca', 'https://texasstation.sclv.com/Dining/Slices-Pizzeria', 'http://www.oldmillgm.ca', None, 'http://www.maac.com/alabama/huntsville/colonial-grand-at-madison?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://www.drbarbaranewman.com', 'http://www.clecabinets.com', None, 'http://www.mcmagain.com/home.html', 'https://locations.theupsstore.com/nc/charlotte/2820-selwyn-ave?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.bloorfitness.com/', 'http://www.kouskousexpress.com', None, 'http://www.sweetalamode.ca', None, None, None, None, 'http://www.globalpestlasvegas.com', None, 'http://www.foliclesalonandspa.com/', 'https://locations.usbank.com/index/nevada/las-vegas/summerlin-smiths-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.givemiacookie.com', 'http://www.chatime.com', 'http://www.therobotoproject.com', 'https://www.bushmillsirishpub.com', 'http://ladlows.com', 'https://sfaservice.com', None, None, 'https://luxxestudio412.glossgenius.com', 'http://www.alankells.com', 'http://www.gianteagle.com/store-locator', 'http://www.marytripi.com', 'http://rajplasticsurgery.com/', None, 'http://www.deltaco.com', 'http://www.steelcitysteak.com', 'http://nickelsdeli.com/saint-laurent/', None, 'http://momentumsalon.com', 'https://octapharmaplasma.com/donor/center/18568', 'http://www.mastercleaners.us', 'http://www.justfresh.com', None, 'https://www.gowireless.com/stores/az/phoenix/phoenix-ahwatukee-foothills/', 'http://shop.helixtelecom.com/', 'http://www.CerberusDesigns.ca', 'http://www.betsysicecream.com', 'https://www.newyorknewyork.com/en/nightlife/pour-24.html', 'http://pinogelato.com', None, 'http://www.vergerlacroix.ca/', 'http://www.starbucks.com/store/113209/', 'http://www.alexreidosleitoes.com', 'http://www.habitatlivingsound.com', 'http://www.attackpestcontrollv.com', 'https://www.kindercare.com/our-centers/mesa/az/000632?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=000632', 'http://www.pawsplaygrounds.com', None, 'http://www.zagg.com', 'https://www.donmillersubaruwest.com', None, 'http://www.ArcadiaCoveApartments.com', None, 'http://www.bodyheattanning.com', 'http://www.litespressobar.com', 'http://www.barbiespetsitting.com', 'http://www.hungryhut247.com', 'http://www.restaurantmochica.com/en/toronto', '1592186182', None, 'http://www.evoautoaz.com', '1592186188', 'http://phochay88.com', None, 'http://www.rockyscustomdetailing.com/', 'http://www.azeyes.com', 'https://www.therackandcue.com', 'http://www.backdoorlv.com', None, 'https://www.capriottis.com', None, 'https://lemonsharkpoke.com/locations/', 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://www.usps.com', 'https://www.labcorp.com', None, None, 'http://www.omzhair.com', 'https://www.marcs.com/stores/marcs-middleburg-hts-southland-grocery-store-4413', None, 'http://woodsrestaurant.ca/', None, None, None, 'http://fourpalmsautosales.com', 'http://gesu.com/', None, 'https://www.purdys.com/shops/details/79', 'http://www.scilv.com', 'http://tjsbutcherblock.com', 'http://aquatherapyclinics.com/', 'https://locations.costavida.com/costa-vida-a2660367671e', 'http://ragingspoon.ca/', 'http://www.queenfishandchips.com/', 'http://www.brownleejewelers.com', '1592186258', 'http://www.gypsybarphoenix.com', 'http://www.tbsstrong.com', 'http://www.titanrelocationservices.com', 'http://www.majormilliken.com/', 'http://www.bestautobuy.com/', 'http://Www.GotGoddessHair.com', 'http://www.cleatswings.com', 'http://outpostcoffee.com', None, None, 'http://www.ampm.com', 'http://www.photoantiquities.org', 'http://www.atmosphere.ca/', 'http://affordablelakenormanshuttle.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'https://stores.mooresclothing.com/ab/calgary/415---3545-32nd-ave--ne.html?utm_source=yelp&utm_medium=listing&utm_content=41&utm_campaign=AB', 'http://www.disciacca.com', None, None, None, '1592186300', 'https://sparklenailsbar.com', 'http://southpointcasino.com/dining/michaels-gourmet-room?cid=ypmic', 'http://www.fiveyearsyoungerfacial.com', 'http://www.thecrepecafe.com', 'http://locations.harristeeter.com/nc/charlotte/205/', None, 'http://www.JohnsonEstateLaw.com', 'http://walmart.com/', None, None, None, 'https://www.pizza73.com', 'https://www.batteriesplus.com/store-locator/az/tempe/batteries-plus-333?utm_source=yelp&utm_medium=local&storecode=333', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', None, '1592186333', 'https://dwss.nv.gov', None, None, 'http://noftz.com', 'https://santanvillage.benefitbrowbars.com', '1592186344', 'http://www.cardiacsolutions.net', 'http://natureworksbest.com/', 'http://www.mdclv.com', None, 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, 'http://www.petsmart.com', None, None, 'http://www.sawhilbanquet.com', 'https://lernerandrowe.com/?utm_source=Yelp', 'http://www.maccosmetics.com', None, 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', 'http://www.timhortons.com', None, 'https://www.rolex.com/rolex-dealers/dealer-locator/retailers-details/rolexboutiquelvluxury.rswi_17986.lasvegas.unitedstates.rolexdealers.com', 'http://www.vosgeschocolate.com', 'http://www.a2zrm.com/', None, None, 'http://www.pittsburghprestigephotobooth.com', 'http://www.carmeldayspa.com', 'http://reddiservices.com/phoenix', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.abcpediatricshenderson.com/', 'http://www.wolsteincenter.com', 'https://stores.chicos.com/s/the-summit-at-scottsdale', 'http://www.monsterpgh.com', 'http://www.soccerzonevegas.com', 'http://www.northhillpizza.com', 'http://www.oxigenspa.com', None, 'https://eyetique.com/squirrel-hill', None, 'http://www.azresearchcenter.com/', '1592186416', 'https://www.cielohendersonapts.com', 'http://www.baileyorthoaz.com/', 'http://www.hobbypeople.net', 'https://www.holidayinn.com/redirect?path=hd&brandCode=hi&hotelCode=clesv&regionCode=1&localeCode=en&cm_mmc=mdpr-_-yelp-_-enhanced_profiles', 'https://mandarinrestaurant.com/mississauga/', 'http://www.switchconsignment.com', 'http://www.porschenorthscottsdale.com', 'http://www.carolinapacknc.com', None, None, 'http://www.guyandgalsalongilbert.com', '1592186443', 'https://www.wilhelmautomotive.com/locations/tatum-ranch/', None, None, 'https://twomenandatruck.com/movers/il/champaign', 'https://castlerents.com', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'http://www.dukescycle.ca', 'http://greatwhaletattoo.com', '1592186463', None, 'http://www.trilliummoving.com', None, 'https://www.dominos.com', 'http://local.buckle.com/AZ/TEMPE/385/?utm_source=Buckle&utm_medium=Website&utm_campaign=Store+Locator', 'http://myorangeleaf.com/frozen-yogurt-store/AZ/chandler/2875-west-ray-rd%2c-suite-1?id=8', 'http://www.17thavechiropractor.com', 'http://www.abiaz.com', 'http://www.thevenetian.com/RIVA.aspx', '1592186483', None, None, 'http://vwnorthscottsdale.com', '1592186491', '1592186493', 'http://www.gordsappliance.com', 'http://www.robinsongarden.com', 'http://www.cityandeast.com', 'http://ccvet.com', 'http://www.treatmentsalon.com', 'http://www.cottonon.com', 'http://fixauto.com/scarborough-town-centre', None, None, 'http://www.whitetoronto.com/', 'http://www.ercfixtv.com', 'http://www.jimmyscoffee.ca', 'http://www.ngvlanes.com', 'https://www.anytimefitness.com/gyms/288/Las-Vegas-NV-89139/?utm_source=yelp&utm_medium=local', 'http://inandoutmoving.ca/', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.madisonavecakes.com', 'http://www.manestudio.ca', 'http://blackcatpgh.com', None, 'http://www.smileshopdental.com', 'https://www1.shoppersdrugmart.ca', 'http://www.bullfrogspas.com', 'http://www.childrenslearningadventure.com/', None, '1592186547', 'http://www.desimoneglobalmarketing.com', '1592186550', 'http://www.timetoronto.com', 'http://restaurant.chineseonlineorder.com/goldengatehenderson', 'http://restaurantletandoor.ca', 'https://www.autozone.com/locations/az/phoenix/3908-e-thomas-rd.html', 'https://www.snapdragon-salon.com', 'http://www.thetamalestore.com', 'http://www.peterpiperpizza.com/', None, 'https://mononabarbershop.com', 'http://www.carolinasdish.com/', 'http://www.sparkleanlaundryphoenix.com/', 'http://www.lagunaspanv.com/', None, 'http://www.foxfamilydental.net', None, '1592186583', 'http://www.usps.com', 'http://www.sprint.com', None, 'http://islandheatdinnershow.com', 'http://flashforwardsites.com', 'http://www.bishoplawoffice.com', 'http://www.grandavenueproduce.com', '1592186601', 'http://www.balconycleaning.net', 'https://www.mapleteahouse.com', None, '1592186607', 'http://www.thechesterfieldshop.com', None, 'https://cftn.com', 'https://stoughtontireandautorepairinc.com', 'http://www.jiffylube.com', 'http://www.starbucks.com/store/9298/', 'http://www.thaidelightaz.com', 'https://www.redmountainweightloss.com/scottsdale/', 'https://www.libertysquare-apartments.com', '1592186628', 'http://guireitoronto.com', '1592186632', None, 'http://k1speed.com/phoenix-location.html?utm_source=Yelp', 'http://www.jasesouder.com', 'http://www.thecalgarygroomroom.com', None, 'http://www.littleones.ca', 'http://www.leagueofvapes.ca', 'http://www.scottsleedmd.com', None, 'http://mex-city.com/', None, 'http://www.azrapidmaintenance.com/index.html', 'http://www.coveredwagonaz.com/', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', None, 'https://www.thepaincenter.com/?utm_source=yelp&utm_medium=referral&utm_content=arizona-gilbert', 'http://ritzasiaaz.com/location.php/', 'http://www.meineke.com', 'http://www.soraonrose.com', None, 'http://www.ritzcarlton.com/en/hotels/canada/toronto', 'http://paradisevalleyseptic.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357318&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://torrancepharmacy.com', None, 'http://www.littlecaesars.com', 'http://www.hummusbowls.com', '1592186689', 'http://www.audioworkx.com/', 'http://restaurantvago.com', None, 'https://www.batteriesplus.com/store-locator/nc/gastonia/batteries-plus-423?utm_source=yelp&utm_medium=local&storecode=423', 'https://beezybooth.com', 'https://www.montecarlo.com/en/nightlife/brand-lounge.html', None, 'http://www.sovarizona.com', 'https://www.orangetheory.com/en-us/locations/arizona/phoenix/2501-west-happy-valley-road-suite-32-1020/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.stylevsalon.com', None, 'https://www.ahn.org/location-detail?name=AGH_Suburban', 'http://shopurbo.com', 'https://www.josbank.com/store-locator/mt-lebanon-pa-356?utm_source=yelp&utm_medium=listing&utm_content=356&utm_campaign=PA', 'http://www.campers-village.com', None, 'http://www.bouldercreekgc.com', None, None, None, 'http://www.bigalscanada.com/stores/locations/NorthYork/northyork.html', '1592186732', None, 'http://www.oakdalepodiatrist.com', 'https://www.penrosecharlotte.com', None, 'http://www.wildwingrestaurants.com/franchisees/brampton-trinity-commons/', 'http://www.scottsdalehillsah.com', 'https://www.sundancecinemas.com/', '1592186748', None, None, None, 'http://www.opticgallerysummerlin.com', None, 'http://www.cottonlanervresort.com', '1592186762', 'http://franklygoodcoffee.com', '1592186767', 'http://www.thebeerstore.ca/locations/sheppardwillowdale', 'https://www.moxieservices.com/locations/phoenix/?utm_source=yelp&utm_medium=cpc&utm_campaign=2019_cpc', 'http://www.valleymedped.com', None, '1592186777', 'http://www.camelotinnelyria.us', 'http://www.kevinpowellmotorsportscharlotte.com', None, 'http://www.spiceasianbiz.com', 'http://www.santabarbaracatering.com', 'https://www.gamestop.com/store/us/wi/madison/740/prairie-towne-center-gamestop', 'http://www.lasvegasspinesurgeon.com', 'http://songbirdartistry.com', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', None, 'https://budgetblinds.com/Goodyear/?utm_source=yelp&utm_medium=naf-listing&utm_campaign=NAF-LOCAL-YELP', None, None, 'https://www.amazinglashstudio.com/studios/nc/charlotte/park-towne-village', None, 'http://www.therollhouse.com/wickliffe', 'http://www.dunkindonuts.com', 'https://www.purebarre.com/location/chandler-az', None, 'http://www.eliteacademyofgymnastics.com', 'http://advancedmetal.com', 'http://www.pitaland.ca', None, 'http://www.evex.ca', None, None, 'https://www.anytimefitness.com/gyms/92/Phoenix-AZ-85048/?utm_source=yelp&utm_medium=local', None, 'https://aamcobayarea.com/locations/concord', 'http://www.starbucks.com', 'http://www.spectrumbrands.com/', None, 'http://www.bellybumpsandbabies.com/', None, 'http://www.theknittingroom.ca', 'http://www.simplesimonpies.com', 'http://www.ohiojunkforce.com', None, 'http://www.publix.com', '1592186858', None, 'http://www.furniturestorelasvegas4u.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://tumbleweedhotel-hub.com/', None, None, 'http://www.polishdnailbar.com', 'http://uppercrustwinebar.com', 'https://www.kfc.ca//store/1595-cote-vertu-st-laurent', None, None, None, 'http://www.25liberty.ca', 'http://www.yehyogourt.com/', 'http://www.lasvegasfloral.com/?srccode=EF_YELP', 'http://www.wigsrustoronto.com', 'https://www.walgreens.com/locator/walgreens-3025+las+vegas+blvd+s-las+vegas-nv-89109/id=6167', 'https://ramclean.com', None, None, 'http://mintlocker.com', None, None, 'http://www.greenfieldgroomingsalon.com', None, '1592186914', 'http://www.tankstap.com/', None, 'http://www.ouestantoniospizza.com', 'http://www.badwaterbrewing.com', 'https://local.albertsons.com/az/chandler/3145-s-alma-school-rd.html', None, None, 'https://quantumcleaning282.wixsite.com/website', 'https://locator.chase.com/ny/glendale/71-04-woodhaven-blvd', None, 'http://www.milestonesrestaurants.com/', None, None, None, 'http://www.wmdouglas.com/charlotte', 'http://www.nvscc.com', None, None, 'http://www.planetdog.ca', 'https://www.arizonarestorativepsychiatry.com', None, None, 'http://www.mevamekitchenexpress.com/', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', None, 'http://nevadaeyephysicians.com', 'http://www.ranchorelaxotogo.com', 'https://hakkasan.com/las-vegas/', 'http://www.dysartdental.com', 'http://stacyannsscissorhands.com', 'https://www.supercuts.com/locations/az/scottsdale/scottsdale-pavillions-haircuts-9672.html', 'https://locations.churchs.com/nv-las-vegas-8616', 'http://www.landmarkautoanddiesel.com', 'http://www.familyvideo.com', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://stores.dickssportinggoods.com/az/scottsdale/1194/', 'http://www.drallenhuioptometry.com/', 'http://www.fabfred.com/locations/ft-apache/', 'http://www.theteakeeper.com/', 'https://agents.allstate.com/juan-deglane-glendale-az.html', 'http://www.ctctree.com', 'http://www.saharaair.com', None, None, None, 'http://www.holtrenfrew.com/store/holt/stores/hr2/VaughanMills', None, 'http://www.bennett2rentit.com', 'https://locations.theupsstore.com/az/scottsdale/16211-n-scottsdale-rd?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=11088&localechange=1', '1592187020', 'http://www.auburnbayvet.com', 'https://www.swiftaviation.com', 'http://www.sundevilauto.com/locations/az/scottsdale/north-scottsdale-25', None, None, 'http://www.pinotspalette.com/southend', 'http://www.pinkynails.ca', 'http://smartrepairsaz.com', 'http://www.lizyhoeffer.com', 'https://www.spiritsandtales.com', '1592187046', 'http://www.greatclips.com/salons/4614', 'http://www.dunkindonuts.com', None, None, 'http://walkinwalkin.com', None, '1592187060', None, None, None, 'http://www.seespotclean.com', 'http://gogreenac.com/', 'https://iworkoncars.com', 'https://silvernuggetlv.com', None, 'http://www.bk.com', 'http://www.mgmgrand.com/restaurants/crush.aspx', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FMSNMW', 'http://www.AbsolutePetCareAZ.com', 'http://www.scrubtastic.com', 'http://broadbentdentistry.com/', 'https://www.bestbuy.com/site/electronics/geek-squad/pcmcat138100050018.c?id=pcmcat138100050018', 'http://www.honmachirestaurant.com', 'http://www.bluearrowrecords.com/', 'http://www.phoenixrackandaxle.com', None, 'http://www.parkcentraldeli.com', None, 'https://www.mygabes.com', 'http://thriftdlux.com/', None, 'http://www.clinicsalveo.ca', 'http://www.pandora.net/en-us/stores/united-states/85254/pandora-scottsdale-quarter', None, 'https://www.sprint.com/storefronts/bd/sprint-north-las-vegas-nv-89032-fcs-4123/?ecid=SEO:Yelp:2020_Q1:LastMile', 'http://www.housemaster.com', None, None, 'http://nodabarkandboard.com/home.html', 'https://www.destinymartialartsacademy.com', 'http://emakravmaga.ca', 'http://www.stateoftheartdesigners.net', 'https://www.chevronwithtechron.com', 'http://www.bigjimsrestaurant.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=626&utm_content=bpas', None, None, 'https://www.lasikvisioninstitute.com/lasik-eye-surgery/cleveland-surgeon-center/?venid=YLP31&subid=CLE', None, '1592187147', None, 'http://www.verizonwireless.com/stores/arizona/mesa/val-vista-204086/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', None, 'http://www.midwoodsmokeshack.com', 'http://www.chapters.indigo.ca', 'https://www.vistasureno.com', 'http://www.therumormillmarket.com', 'http://www.drywallperfection.com', '1592187163', 'http://artscapeyoungplace.ca', 'https://www.supercuts.com/locations/oh/rocky-river/rocky-river-haircuts-81630.html', 'http://www.katieskorner.com', 'http://www.camh.net', 'http://www.southwestfunctionalmedicine.com', None, None, 'http://www.lionsmanegrooming.com', 'http://www.amazinginc.net', 'https://haircutmenfairlawnoh.com', None, 'http://www.cherryberrieslasvegas.com', 'http://www.shopwoc.com', 'https://www.amcofdv.com', 'http://www.starbucks.com/store/10759/', 'http://usmaniagrill.ca', 'http://www.igoturback.com?cmpid=GSDG_BLM_0006', 'http://www.cal-am.com/communities/chaparral-village', 'http://azmajorsoccerleague.com', None, 'http://www.valleygoldmine.com', 'http://www.saludjuicery.com/aspinwall/', 'http://www.undefeated.com', None, 'http://www.whatalesya.com', 'https://www.burialplanning.com/cemeteries/resthaven-memory-gardens/', 'http://collegestreetanimalhospital.com', 'http://pueblosereno.com/', 'http://www.autonationbuickgmchenderson.com', None, 'http://fortmill.burnbootcamp.com/', 'http://www.orangedumpster.com/', 'http://portofsubs.com', 'https://www.newdermamedlaserclinic.com', None, None, 'http://www.svmmjcc.com', 'https://stores.bareminerals.com/wi/madison/us-2313/', None, 'http://www.rdquake.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.sears.com', None, 'https://www.storage-solutions.org/storage/arizona/storage-units-peoria/8266-W-Lake-Pleasant-Parkway-115', 'http://www.darinaelectrolysis.ca', 'https://www.allamericanpubclt.com', 'http://www.sasshoescharlotte.com', 'http://taylormadecustompools.com', 'http://www.kitchen73.ca/laval', 'http://colorworkslandscape.net', 'http://www.bodyrestorationmassage.com', 'http://fujiyamacalgary.com', 'http://www.castleapartments.net', 'https://www.myeyedr.com/locations/independence-boulevard?utm_source=Yelp&utm_medium=Referral&utm_campaign=independence-boulevard', 'http://carlretterdebtattorney.com', None, 'https://zelaya-jr-painting.com', 'http://www.swarovski.com/Web_CA/en/index', 'http://www.trapezeu.com', None, 'http://www.marshallsonline.com', 'http://kokofitclub.com', 'https://www.thirdfederal.com?=ad.doubleclick.net/ddm/clk/458420725;262568795;w', 'http://www.tropicalsmoothie.com', 'http://www.jonesysclassiccleaners.com/', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', None, 'http://tradelandsaz.com', None, 'http://www.sweetfixbakery.com', None, 'https://www.cellphonerepair.com/charlotte-university-city-nc/', 'http://www.happyvalleyplumbingllc.com', 'http://www.oneofakindpets.com/', 'http://jacksonswash.com', None, None, 'http://www.talkingstickresort.com/spa.aspx', 'http://nathansfamous.com', 'http://fiveguys.com/', None, None, None, None, 'http://christensenconstruction.net', '1592187329', 'http://www.realliving.com/sj-fowler-real-estate', 'http://www.gnargnartours.com/', None, 'http://www.apachestone.com', 'http://www.doddsdoors.com', 'http://www.subway.com', 'http://www.canyon-pt.com/location/surprise-office/', 'http://trustarts.culturaldistrict.org/production/37630', None, 'https://stores.savers.com/nv/lasvegas/savers-thrift-store-1047.html', 'https://milk-n-more.business.site', None, 'http://www.sfldentistry.com', 'https://extremewheels.com', None, 'http://www.JimmyJohns.com', None, None, None, 'https://www.thehouseofused.com', 'http://www.nhhuntersvillepedsandim.org', 'http://www.origintmassage.com/', None, 'http://www.hskaraoke.com', 'http://mesa.floorstogo.com', 'http://www.nveyesurgery.com', 'http://www.stoutflooring.com', None, None, 'https://square.site/book/0GPTRC4PSJ0WB/sunny-girl-spray-tan-phoenix-az', None, 'http://www.leanonmeals.ca', 'http://www.colossusgreektaverna.com/locations/colossuspc/contact/', 'http://sonoranserenityspa.com/', '1592187400', 'http://www.blm.gov', 'https://thrifty.com/loc/ll/CA/OT/TORONTO-~-FRONT-ST-(OT)/330-FRONT-STREET-WEST', 'http://www.benchworksteering.com/', 'http://visit.brownmackie.edu/SERCH/dynamic/bmc-3-step.aspx?RIFID=3322&source=YELP&sourceCode=YELP&cid=SERCH_BMWA_096_SRCH_002&SearchEngine=Yelp&utm_source=Yelp&utm_medium=cpc&utm_campaign=Yelp', None, 'http://www.suzannewigginton.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.carepatrol.com/', '1592187418', None, None, 'http://artgeckoshop.com', None, None, None, 'http://www.loftsonthomas.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/pa/turtle-creek-4072.html?mcid=iyp:8368400', None, 'http://www.thebierhausbistro.com/', 'http://www.wheatbyjay.ca', None, None, None, '1592187446', '1592187449', None, 'http://brathausaz.com/brat-haus-events/', None, 'http://www.stardustbuilding.org', None, 'http://www.blackcanyonconferencecenter.com', 'http://www.pittsburghyellowcab.com', None, 'http://www.casbahrestaurant.ca', 'http://www.solosmallmotors.ca', 'http://www.empirepizzabar.com', 'http://www.jacksonswash.com/location-84th-avenue', 'http://www.dakinemobiledetailing.com', 'http://www.adrenalinetoronto.com', 'http://www.drlockney.com', 'https://locations.churchs.com/az-phoenix-681', 'http://venues.calgarystampede.com/venues/bmo-centre/', 'https://bikanersweetsandrestaurant.ca', '1592187485', None, 'http://www.prayosha.ca/', None, 'http://blackcanarycoffee.com', 'http://www.massagewellvegas.com', 'http://www.brookdaledentalcare.com', 'http://www.mcdonalds.com', None, 'http://www.customcaninecompany.com', 'http://www.dcslv.org', None, 'http://www.terribleherbst.com/', None, None, None, None, 'http://gocheckers.com/team/game-guide', 'http://paradisemelts.com', 'http://www.tribebarrestudio.com', 'http://www.fuguasian.com/menu.aspx', None, None, 'http://www.billygrahamlibrary.org', 'http://www.purolator.com/purolator/ship-track/find-location.page?location=ridRC0715', None, 'http://www.fedex.com', None, 'https://www.snwa.com', 'http://www.freshandeasy.com', None, 'http://www.orthopaedicspecialists.org', None, 'https://www.kwiktrip.com/Locations/Details/650', 'http://www.phoenixbedbugexpert.com', None, 'http://www.videoconversionexperts.com/', 'https://www.cash1loans.com/locations/arizona/phoenix-thomas.aspx', 'http://local.firestonecompleteautocare.com/ohio/cleveland/6874-pearl-rd/?lw_cmp=IYP_YPC_MLP_1694', 'http://www.canadiantire.ca/en/store-details/on/warden-eglinton-on.store.html', '1592187562', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://supremetouch15.wixsite.com/supreme-touch/contact', 'http://www.perryellis.com?utm_source=Yelp&utm_medium=Social&utm_campaign=PE_Yelp_BioCTA', 'http://www.mrtire.com', None, 'http://www.sunbirdgolf.com', None, 'http://www.mocca.ca', 'https://www.pizzaville.ca/stores/hours/2889-derry-road', None, 'http://www.maranellocafe.ca', 'http://www.torontosteamnclean.ca', 'http://www.jogoyaseafoodbuffet.com/', None, 'http://www.joefresh.com', 'http://ladolcepesca.com', 'https://www.theshadestore.com/showrooms/nevada/las-vegas?utm_source=yelp&utm_medium=cpc', 'http://www.tristatetowingandrecovery.com', None, '1592187599', 'http://www.royalvinewinebar.com/', None, 'http://SecondsCity.com', 'http://www.ljsilvers.com', None, 'http://scacciaunion.ca', 'http://truhitfitness.com/north-phoenix/', 'https://orlandoautobody.com', 'http://www.coyoteoaties.com', 'https://www.jiffylube.com/locations/az/phoenix/2098', 'http://www.bigmanspizza.ca', 'https://www.dogtrainer-charlotte.com', None, None, 'http://www.goodwillaz.org/location/goodwill-mckellips-mesa/', 'http://www.azspinalcare.com/', 'http://www.ranee.ca', 'http://www.thecornflower.com', 'http://www.springspreserve.org', None, 'http://www.dakotamoversaz.com', None, '1592187645', 'http://www.bownesshealthfood.ca', 'https://rapidresponders.com', None, 'https://amazingleakdetection.com', None, 'http://www.midas.com/cleveland/store.aspx?shopnum=6355&dmanum=212', 'https://www.fountainpalmsapts.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=organic', 'http://www.bojangles.com', 'http://www.themagicshoplv.com', None, 'http://www.sewmuchfun4you.com/', None, 'http://www.hickorynutgolfcourse.com', 'http://www.mrsbridalboutique.com/', 'https://www.harveys.ca', 'http://www.AZLawnGuys.com', '1592187676', 'https://www.spencediamonds.ca/location/calgary-ab/?utm_source=Yelp&utm_medium=Display', 'http://www.LasVegas1RealEstate.com', None, 'http://www.samosafactory.com', 'http://www.thebrubakerspub.com', None, 'https://www.homestreet.com', 'http://www.nikosgardening.ca/', None, 'https://www.victra.com/?utm_content=Yelp&utm_medium=URL&utm_source=Yelp', 'https://www.mindbodhiyoga.com', 'http://www.virginamerica.com/', None, None, 'http://www.health-a-licious.com', 'http://lacampagnaonline.com', 'http://www.canampm.com/sun-valley-ranch', 'http://www.ranefamilyinsurance.com', None, 'https://stores.nyxcosmetics.com/directory/nv/las-vegas/3663-south-las-vegas-blvd.html', 'http://trilogycle.com', None, 'http://www.bloomersto.com', 'https://www.walmart.com/store/5334/aurora-co/details', 'http://www.fithcc.com', None, 'http://99only.com/store/Las-Vegas---Beltway/', '1592187730', None, 'http://www.vbinspect.com', 'http://www.makinolasvegas.com', None, 'http://samspizza.co', 'http://www.swimmerinsurance.com', 'http://www.lipsboutiquebyjka.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', None, 'http://www.themarvelexperience.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.bannerhealth.com/locations/banner-urgent-care-6', '1592187760', 'http://www.taitjointreplacement.com', None, 'https://www.weecarelv.com', None, 'http://www.pizzanova.com', None, None, 'http://www.entebellamedical.com', 'http://www.deansgreenhouse.com', 'http://www.jazz.fm', 'https://locations.churchs.com/az-phoenix-7235', 'http://www.hashhouseagogo.com/', 'https://www.wyndhamhotels.com/hotel/15081?tel=18008899735&iata=00093785&cid=fe:hj:20170523:yl:pp:hjus:15081', 'http://www.hawaiianbarbecue.com', None, 'http://www.pizzahut.ca/', None, None, 'http://www.hawaiipoke.ca', None, 'http://www.bogdananghelmd.com', 'http://www.thegreenhousetavern.com', 'http://www.farmgirlsfood.com', 'http://www.museums.nevadaculture.org/nsmlv-home', 'http://www.graysbooks.com', None, 'https://www.clubpilates.com/fortmill', 'http://www.swc', 'http://www.4feldco.com/locations/madison/', 'https://www.simon.com/mall/arizona-mills/stores/disney-store-outlet-the', None, 'http://www.raymillphotography.com', 'http://www.thomasyu.ca', None, 'http://www.animalinnlv.com', None, None, 'http://www.ajlawplc.com', 'http://www.metrobark.com', 'https://www.get-go.com/', None, 'http://www.clevelandairport.com', None, 'http://jbamotors.com', '1592187838', 'http://www.wagonthedanforth.com/', None, 'http://www.toryburch.com', 'https://samurairamen-sushi.com', None, 'http://pizza.dominos.ca/Mississauga-Ontario-10348', 'http://www.universalscreenarts.com', None, None, None, 'http://www.keybank.com', None, 'https://cannacabana.com', '1592187864', 'http://www.sweetpeas.ca', 'http://cornercafewi.com/', 'http://www.restaurantbellissimo.com/fr', 'http://pigtailsandcrewcuts.com/charlotte-cotswold', None, 'http://www.calldanielhull.com?cmpid=F27M_BLM_0006', 'http://www.sidestreetpubandgrill.com/', None, 'http://www.DesertFitnessAZ.com', 'http://www.beardedchefaz.com', 'http://www.WickedBakery.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.gumbyspizzamadison.com/', None, None, 'http://www.makeafoodiecall.com', 'http://www.dunkindonuts.com', None, 'https://www.shadowmountaindentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.biennails.com', 'https://www.americasbest.com/store-list/avon-oh-44011/', 'http://www.wynnlasvegas.com/#Shopping/blacksatin', None, None, 'http://farmersagent.com/gelfond', None, 'http://cherryblossompools.com', 'http://www.eatnpark.com', None, 'http://www.activekidspediatrics.com', 'https://daisybluesummit.business.site', 'http://www.cedarcenterhardware.com/', 'http://www.hectorsmovingservices.com', 'http://locations.maurices.com/nv/lasvegas/clothing-stores-lasvegas-nv-1751.html', None, None, 'http://www.sonoramesquitegrill.com', 'http://www.airbornetrampoline.ca/locations/woodbridge/', 'https://www.enterprise.com/en/car-rental/locations/us/az/mesa-alma-gardens-5050.html?mcid=iyp:8368400', 'https://arizonaorganix.org', 'http://www.coinlesslaundry.com/23rd.html', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://littlerascalslearningcenter.com', 'http://www.barreljunction.com/location', None, None, '1592187957', None, None, 'http://www.kensingtonmakeupacademy.com', 'https://www.greulichs.com', None, 'http://www.eastwinddentallv.com', None, 'http://www.metroparktune.com', 'https://locations.theupsstore.com/az/gilbert/70-s-val-vista-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.trinitycathedral.com', 'http://kokosmiles.com', None, 'http://www.millerswaterdamageandrestoration.com/henderson-nv.html', None, 'http://ltgrill.com/', 'https://eastvalley.bintheredumpthatusa.com', 'http://www.swgas.com', 'http://www.FletcherHeightsAH.com', None, 'http://www.mooredalesailing.com', 'http://www.disgraceland.ca/', 'http://www.michaelkors.com/stores/united-states/nv/las-vegas/michael-kors-palazzo', None, 'https://www.kurevapes.com', 'http://www.sossystems.com', None, None, 'https://stores.petco.com/nc/gastonia/pet-supplies-gastonia-nc-1586.html', None, 'http://www.Azbiltmorebarbershop.com', 'https://www.zaxbys.com/locations/nc/concord/7781-gateway-ln-nw/', '1592228118', 'http://eyelovebeautybar.com/', 'http://www.justrolldup.com', 'http://www.7-eleven.com/?yelp=22886', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___estrella', None, 'https://www.gostorageone.com/self-storage/nv/las-vegas/maryland-pkwy/', 'http://www.cineplex.com/Theatre/cineplex-odeon-ajax', None, None, None, 'https://www.zimbrickhonda.com', 'https://locations.jackinthebox.com/us/ca/glendale/1200-w-glenoaks-blvd', 'http://www.kgautoworkspgh.com', 'https://www.americafirst.com/about/branches/branch-details.cfm?siteNo=104', 'http://www.goldenwestmanagement.com/', None, None, 'http://www.adega9.com', 'http://www.freshandwild.ca', 'http://www.scottsdalerestaurants.co', None, 'http://headtotoeinc.com', 'https://theeggworks.com', 'http://www.aqualunch.ca', 'http://www.steakonastone.us', 'http://www.thesavannah.com', None, None, 'http://www.ktnv.com/', None, 'https://honeycombsaloncollective.com', None, 'http://sunwest-az.com', 'http://www.rustikrotisserie.com', 'http://www.eliesfamilyrestaurant.com', 'https://www.lennar.com/New-Homes/Nevada/Las-Vegas/Las-Vegas/Mountains-Edge/Monterey-Ranch-The-Gardens/INHC', 'https://playgroundsdartzone.com', 'https://stores.peoplesjewellers.com/on/markham/5000-highway.html?cid=YEXT', 'http://www.tuttisantibynina.com', 'http://www.redsealnotary.com', 'http://www.cheekychicbb.com/', None, None, None, 'http://www.garciabailbonds.company', 'http://www.el-chameleon.com', 'http://www.miamistarglo.com', 'http://www.felinefabulous.com/', 'http://firebyjames.com', 'http://www.lumiermedicalspa.com', 'https://www.thaithaispaandmassage.com', 'http://www.lisaeleyphotography.com', 'https://corebodypilatesaz.com/locations/north-gilbert-pilates-studio', 'https://stores.thenorthface.com/NV/LAS-VEGAS/USA314/', 'http://local.firestonecompleteautocare.com/ohio/rocky-river/21210-center-ridge-rd/?lw_cmp=IYP_YPC_MLP_2089', 'https://leancanteengcu.wixsite.com/healthy', 'http://www.hargta.com', 'http://www.vanish-ink.com', 'http://www.elsombrerovegas.com/', 'http://www.SkatelandMesa.Com', 'http://www.aiellospizza.com', 'https://www.tristastevensonstylist.com', 'http://www.marisolcu.org/', 'http://www.theforumbarpar.com', 'http://www.usps.com/', None, 'https://www.carcolv.com', 'http://www.blacks.ca', 'http://barredefinitions.com', None, 'https://nailsatthelakes.business.site/?m=true', None, 'http://www.menschssecurityfilms.com', 'https://hovdeproperties.com', 'http://www.carolinasmedicalcenter.org/body.cfm?id=14', None, 'http://www.dentproaz.com', 'http://www.littlebangkokthairestaurant.com', 'http://thegallerysouthend.com/', 'http://www.desertsandsrvresort.com', None, None, 'http://www.townofyork.com', None, None, 'http://www.onedaytours.com', None, 'http://www.abercrombie.com', None, None, 'http://www.elpolloloco.com/locations/store/3859', 'https://dripedgeroofing.com', '1592228355', '1592228358', 'http://www.sleepnumber.com/?utm_source=Yelp&utm_medium=CPC&utm_term=CTA&utm_campaign=9f4Lf6iyxkIXfQw-hozi2w&cm_mmc=Yelp-_-Yelp-_-WebsiteLink-_-9f4Lf6iyxkIXfQw-hozi2w-904825&tag=904825', None, 'http://www.fairviewmall.ca/EN/Directory/Stores/Pages/NormaReed_1084A.aspx', None, None, None, '1592228370', 'http://www.qualityhomeinspectionspittsburgh.com/', 'https://mattressbyappointment.com/locations/nv/lasvegas/', 'http://retinanevada.com/', '1592228381', 'https://drcooperortho.com', None, 'http://www.brookcreekapartments.com', None, 'https://www.chevronwithtechron.com', 'http://www.citi.com', '1592228400', None, 'http://www.hobobillstrainhousellc.com', 'http://www.maidstr.com', 'http://www.teavana.com', 'http://www.webuycars.com/location', 'http://drphonerx.com', 'http://www.jaquelineandrea.com', 'http://sc-clinic.com/clinic/bay_and_college/', 'http://www.quailhollowresort.com/page/dining', None, None, 'http://www.chtools.ca', 'http://www.silvercollectionatthepark.com/?utm_knock=y', None, 'http://www.nvcoin.com', None, 'http://www.petco.com', None, 'https://www.giggles.ca/fr', 'https://www.associatedbank.com/location/WI/madison/2001-londonderry-dr', None, 'http://www.cascadeautogroup.com', 'https://eatcopperbranch.com', 'http://www.ZahlerProperties.com', 'http://www.somethinscooking.com', 'https://www.levinfurniture.com/furniture-store/oh/mayfield-hts/6051-mayfield-rd', '1592228466', None, 'http://www.bvinsurance.ca', None, 'http://www.csn.edu/library', 'http://www.waxon.ca', 'https://www.davidsbridal.com/?utm_source=Yelp&utm_medium=OrganicSearch&utm_term=84&utm_content=DisplayURL&utm_campaign=WebsiteListing', 'http://affyspremiumgrillscarborough.com', 'http://www.asapcity.com', '1592228491', 'http://www.libertymutual.com/insurance-office-madison-wi', 'https://www.ihop.com/en/restaurants-south-las-vegas-nv/7490-s-las-vegas-blvd-3096', None, None, 'www.ripspub.com', 'https://melodys-chair.business.site/#gallery', 'https://www.upack.com', '1592228513', 'http://www.customcoaches.ca', 'http://www.midabui.com', 'http://www.bostonsgourmet.com/', 'https://www.arrowheaddentalgroup.com/?sc_cid=yelp:o:listing&_vsrefdom=yelp', 'http://www.saberhealth.com', None, 'http://www.trainersclubaz.com', 'http://acdentalvegas.com', 'http://www.crateandbarrel.ca/Stores/Store.aspx?storeid=201', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'https://impactptaz.com/scottsdale/', 'http://choicehotels.com/Suburban', None, '1592228544', 'http://www.plasticmaninc.com', 'http://www.mnmshop.com', None, 'http://www.desertstorage.com/scottsdale-az-storage-units', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', None, 'http://www.clubmonaco.ca', 'https://parkwoodslaundry.com', None, None, '1592228568', None, 'http://venushomesaz.com', None, None, '1592228579', 'http://fabulousfloorscleveland.com', 'http://www.clorebeauty.com/', 'http://bluediamondbestbitedental.com', 'http://www.wildeeasttownehonda.com', None, None, 'http://www.bootmaster.com', 'http://www.freevegasclubpasses.com/yelp', 'http://www.planetfitness.com/gyms/glendale-downtown-az-1110?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://booyah-inc.com', 'https://locations.wendys.com/united-states/nv/las-vegas/9385-south-eastern', '1592228604', 'https://www.autonationbuickgmcwestsahara.com', None, 'http://www.highlandparkclubapartments.com', 'http://www.russellaquatics.com', 'http://www.eatatbobsdiner.com', 'http://www.huffsautomotive.com', '1592228619', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', None, 'http://www.freds-flowers.com', 'http://www.handandstone.ca/locations/jarvis-adelaide', 'https://www.azmobiletanning.com', None, 'https://www.audinorthlake.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', None, 'http://www.bunkhousekids.com/', 'http://www.flooringamericaofchandler.com/', 'http://bestbridalandtuxedo.com/', 'http://mcghies.com', None, 'http://www.lhsstudio.com', 'http://summerlinsmiles.com', 'http://alfornopizza.com/', 'http://www.thebatteryguy.com', 'http://www.piola.it', 'http://www.thaihousecalgary.com', None, 'https://agents.allstate.com/rosalie-gonzalez-las-vegas-nv1.html', 'https://www.champssports.com', 'http://www.greenlifecafemadison.com', None, None, None, 'http://www.napolipizzasqhill.com/', 'http://www.amptover.com', 'http://www.bronzecafe.com', 'http://www.envisionnv.com', None, 'http://www.conspirephoenix.com', 'http://findlayhonda.com', 'http://www.LendingPathway.com', None, None, 'https://www.walmart.com/store/2768/mesa-az/details', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://islingtongolfclub.com', None, 'http://HealthySkinLasVegas.com', 'http://cherryst.ca/', 'http://www.popsexotics.com', 'http://StrawberryPropertyManagement.com', 'https://www.extraspace.com/storage/facilities/us/pennsylvania/west_mifflin/1000000568/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', None, 'http://floresdecoloresart.com', 'http://www.chicos.com/store/home.jsp?cmp=MOC_yelp', None, None, 'http://www.cbdamericanshamanlv.com', None, 'http://www.sheacoco.ca', 'http://dollarcanada.ca', 'http://www.sapphirerealtyaz.com', 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://greenwithenvyaz.com', None, None, 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'https://www.redlobster.ca/locations/list/on/toronto/20-dundas-street-west', 'http://lemodernjapanese.com', 'http://www.edwardsmovinglabor.com', 'http://www.deforestfamilyrestaurant.com/', 'http://www.stusmotorcycletowing.com', 'http://www.foxpeterson.com', 'http://luckyspizza67.com', 'http://www.catboardingcharlotte.com/', None, 'https://familybraces.ca', 'http://www.letsdodinneronline.com', None, None, 'http://allstarhairnailslasvegas.com', 'http://www.coldstonecreamery.com/stores/22323', None, 'http://www.straightedgewallpapering.ca/default.htm', 'http://www.tsalonmesa.com', 'https://spiceclub.foodticket.ca/foodticket/cgi/bestel.cgi', None, 'http://mardaloopwellness.com', 'http://www.vegasCapital.com', 'http://7eleven.ca/store-locator/33259', None, 'http://shaggychic.com', 'http://www.chicagodeepdishpizza.com/contact-us/calgary-ne', 'http://www.abbott-trophies.com/', 'http://www.aspca.org', 'http://archibaldmicrobrasserie.ca/index.php/fr/restaurant-blainville.html', 'http://cpm-apts.com', None, None, 'http://poshnailscharlotte.com', 'http://www.sallybeauty.com/', 'https://www.4wheelparts.com/stores/ohio/4wp-cleveland-oh-51', 'http://www.davesducts.com', None, None, 'http://www.trianglerealty.us', 'http://www.findlaychevy.com/', 'http://mountainpie.com', 'http://www.Districtlending.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://www.redmangousa.com', 'http://wtfexp.com', 'http://www.mi5tentertainment.com', None, 'https://www.bmoharris.com', 'http://www.ymcacharlotte.org', None, 'http://sphinx-cafe.com/', '1592228860', 'http://subway.com/', None, 'https://stoneandvine.com', 'http://www.papajohns.com', None, 'http://www.deltaco.com', 'http://illinishop.com', 'http://www.canadiantire.ca/en/store-details/on/warden-eglinton-on.store.html', 'http://medifastarizona.com', 'http://www.amorino.com', 'http://pdmtailor.com', '1592228887', 'https://www.casamiascottsdale.com', None, 'http://www.paragonphysicaltherapy.com', 'http://www.newviewrealtygroup.com', None, 'http://charlotteorthodontists.com/', 'http://www.clarkcountycourts.us/', 'http://www.redspaceevents.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://www.steaknshake.com/locations/23413-steak-n-shake-kenyon-road-urbana', 'https://www.cresthavengolf.ca', '1592228921', 'https://locations.wendys.com/united-states/ga/brunswick/164-altama-connector', 'https://www.palladiumeventcenter.com', None, 'http://www.royalganesha.com', 'http://mlk-smog-check.business.site', 'http://www.wemovewi.com', None, None, 'http://www.stevensplumbingac.com', 'http://akronfitnessandwellness.com/', None, 'https://www.wellsfargo.com', 'http://www.portofcleveland.com/environment-infrastructure/cleveland-lakefront-nature-preserve/', 'https://ad.doubleclick.net/ddm/clk/434046915;236895156;q', None, 'http://tiltedkilt.com/richmond-hill/', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.investarrealestate.com/agent?xid=040101-01&name=Jacqueline-Kenoun', 'http://www.mirage.com/casino/race-and-sports-book.aspx', None, 'http://www.lilacbakeryaz.com', 'http://www.vegasvalleyphotography.com', 'http://desertmesapainting.com', 'https://www.chick-fil-a.com/arboretum', None, 'http://www.usmenuguide.com/honmachi.htm', 'http://www.cox.com', 'http://www.sgi-usa-lasvegas.org/', 'http://www.pancho-and-leftys.com', 'http://www.shell.com/', 'http://www.lofthairlounge.ca', 'https://www.metro.ca/trouver-une-epicerie/44', None, None, 'http://www.vfwpost3513.com', None, 'https://lasvegasurology.com', 'http://www.animalhousevetqueencreek.com', 'http://www.CLTvictor.com', None, None, 'https://www.shearexcellence.com/dilworth/', None, 'https://www.choicehotels.com/CN803?mc=blypypaf', 'https://thejoyfullkitchen.com', 'http://www.dbksalon.com', 'http://qdoba.com', None, 'http://www.francescasfaceliftoflasvegas.com', None, None, 'https://local.safeway.com/safeway/az/gilbert/90-s-val-vista-dr.html', None, None, 'http://massagemaniaglendale.com', 'http://www.chivino.com', None, 'http://www.integritytransportationpgh.com', None, 'http://www.dynastybuffetnc.com', 'http://www.dvf.com/', 'http://www.casitassanmarcos.com', 'https://sincitymoto.com', 'http://www.bodyandsoultherapy.ca', None, 'http://www.grapevinecabinets.com', 'http://www.arizonadanceartistry.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___metro_ii', 'http://www.nps.gov/jaga/', None, 'http://www.foothillsautoglassphoenix.com', 'http://www.iloveichibanaz.com', None, None, None, 'http://lahainagrillLV.com', 'http://www.adcopaint.com', None, 'http://everydaycafepgh.com', '1592229087', 'https://desertcastlepc.com', 'http://www.stonecreekroofingaz.com', None, None, 'http://www.bfshomewarranty.com', 'http://thomashinds.ca', 'http://www.dermatiquemd.com', 'http://www.bathemp.ca', 'https://nice-garden-landscape.business.site', 'http://www.browart23.com/location.html', None, 'http://www.millerframe.com', 'http://www.JimmyJohns.com', 'http://www.fabriziovegas.com', 'http://chensnoodlehouse.business.site', None, None, 'http://www.ridersinn.com', 'http://www.radjewellery.com', 'https://www.statefarm.com/agent/us/az/phoenix/eric-jackson-x4xfz21d000?cmpid=r6sy_blm_0006', 'http://yelp.com/elite', 'http://www.itsabaotime.ca', 'http://www.azchoicechiro.com', 'http://www.apple.com', '1592229145', 'http://www.superstarcarwashaz.com', 'http://futuredirectionsspa.com', 'http://www.heatherkphotography.net', 'http://www.cvcheart.com/scottsdale-princess-office/', 'http://jfkfinancial.com', 'http://www.canadiantire.ca', None, None, None, '1592229167', 'http://www.samuraicomics.com', None, 'https://nationwidevision.com/location/las-vegas-vision-center-silverado-ranch', '1592229176', None, 'https://ad.doubleclick.net/ddm/clk/435408715;237471434;h?https://www.hrblock.com/block-advisors/local-tax-offices/arizona/gilbert/67-s-higley-rd/2404?otppartnerid=9308&campaignid=pw_mcm_9308_9763', 'http://www.menchies.com', 'https://www.getpreloved.com', 'http://www.thainaka.ca/', 'http://retail.monroehardware.com/', 'http://cualv.com', 'http://www.starbucks.com', 'https://www.pteglv.com/locations/sean-patricks/deer-springs-5th-st/', 'http://www.mooseandbeargrill.com', 'http://assortedtablewine.com', '1592229204', 'https://www.haircutmenblakeneycharlottenc.com', 'https://www.basculebrewpub.com', 'https://www.aramarkuniform.com/our-locations/aramark-uniform-services-phoenix2', None, 'http://myloannailslasvegas.com', 'https://www.walmart.com/store/1093/rantoul-il/whats-new', None, None, None, None, 'http://www.mrsub.ca', 'https://www.metropcs.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.francisandsonscarwash.com/category/7889/francis-and-sons-car-wash-of-peoria-az.htm', 'http://www.swisschalet.com', None, 'http://www.nail-pretty.com', 'http://www.southernhighlandscyclery.com', None, 'http://www.wpxi.com', 'http://docromeopark.tk', 'http://guitartreemusic.com', None, 'http://www.dennysallnighter.com/', 'http://www.queencityclosets.com/', 'http://onestopnutrition.com', 'https://www.flavours-ajax.com', None, None, 'https://heightspestcontrol.com', 'http://vsnails.com', 'http://www.desertflowerseniorliving.com', 'http://www.reclaimedart.org', 'http://www.drdonnawoo.com/', 'https://www.sunsetgrill.ca', 'http://cuttingedgebarbershoplv.com', 'http://www.lllreptile.com/', 'http://www.cencispizza.com/wexford', '1592229284', 'https://www.gowireless.com/stores/az/scottsdale/scottsdale-scottsdale-fiesta/', 'http://haneysfamilyjewelers.jewelershowcase.com', 'http://www.evpools.com', None, None, 'http://www.activatechiropracticclinic.com', 'http://glendale.mensvitalitycenter.com/', 'https://www.potterybarn.ca', 'http://www.learningexpress.com/store/robinson/', 'http://www.letzrolloffroad.com', 'http://quickresponseplumbing.ca', 'http://hamptoninn3.hilton.com/en/hotels/arizona/hampton-inn-and-suites-phoenix-goodyear-PHXGYHX/index.html?SEO_id=YELP-HP-PHXGYHX', None, None, 'http://www.districtflats.com', None, 'http://www.urbanashop.com', None, 'http://www.goodwill.org', 'http://lvfurnituredirect.com', 'http://locations.maggianos.com/us/ohio/beachwood/beachwood', 'http://www.mobil1mentor.com', 'https://cocofreshtea.ca', 'https://www.uhaul.com/Locations/Truck-Rentals-near-Gilbert-AZ-85234/922024/', '1592229337', None, None, 'http://bk.com/', '1592229346', 'http://hkrealtygroup.com', 'https://www.sparkletts.com', None, 'http://isabelcleaning.blogspot.com/', None, None, 'https://www.jackentertainment.com/cleveland/', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'https://www.90degreesapartments.com', None, 'http://www.fourlakesfamilydental.com', None, 'https://www.choicehotels.com/north-carolina/matthews/sleep-inn-hotels/nc032/rates', None, 'https://valleywiderestoration.com', None, 'http://fitnesstogether.com/matthews?utm_source=Yelp%20Web&utm_medium=Yelp%20Web&utm_campaign=Yelp%20Web', 'https://www.albertsons.com/home.html', None, 'http://www.bk.com', 'https://www.videogameswap.ca', 'http://www.summitdentallv.com', 'http://pekingman.ca', 'http://ismiledentists.com', 'http://handymanphoenix.com', None, 'http://www.vocellipizza.com/pleasanthills_pa', 'https://stores.sportsmans.com/sportsmans-warehouse/us/az/avondale/10145-w-mcdowell-road', 'http://bennybbq.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://thepetclub.com', 'http://www.zuppasdeli.com/', 'http://bacusbroshotdogs.com', 'http://www.toysrus.com/family/index.jsp?categoryId=2255956&camp=MISC:yelp:store:page:tru:111910', 'http://www.cityofmadison.com/parks/parks/park.cfm?id=1207', None, 'http://www.dominos.com/', 'http://www.mindfulmotionphysicaltherapy.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.centralonbroadway.com/', 'http://www.stashcharlotte.com', 'https://locations.sonicdrivein.com/sc/tegacay/3039-highway-160.html', 'http://www.jtblandscapers.com/', 'http://www.exxonmobilstations.com/1721617-tesoro-62540-las-vegas#_62540-mobil-las_vegas', 'http://www.newimagephotography.com', '1592229448', 'http://sweetvirginiawax.com/', None, 'http://www.perfectflooringpgh.com', 'http://www.macmediainc.com', 'https://alohanailsblakeney.com', 'http://www.rinaldisdeli.com', 'http://www.wizardworld.com/cleveland.html', 'http://www.restaurantcrescendo.com/', None, 'https://www.performancemuffler.net', None, 'http://royal10cigar.com/', 'http://ashavecomics.com', 'http://www.brdiamondsuite.com', 'http://www.laurasecord.ca', '1592229483', 'https://5thavedeliandgrill.com', '1592229487', 'https://www.simon.com/mall/south-hills-village', 'http://www.positivechanges.com', 'http://www.aeacarizona.com', 'http://ajiichibansushi.com/', 'https://www.clearchoice.com/locations/dental-implants-las-vegas/?trans_id=webdisyelp&utm_campaign=Yelp&utm_source=YelpListing&utm_medium=Listing', None, 'http://www.dunkindonuts.com', None, 'http://www.superpumper.com', '1592229508', 'https://www.stance.com/retail/stance-scottsdale', 'https://www.tombstonetactical.com', 'http://www.lebouquetfloristandgifts.com', 'http://www.azmagician.com', 'http://www.whitehouseblackmarket.com/store/home.jsp?cmp=MOC_yelp', 'http://www.monroevillechryslerjeep.com', 'http://www.familylifecenters.org', 'http://locations.harristeeter.com/nc/charlotte/205/', 'http://365gymllc.com', 'https://milios.com', None, 'http://www.padellaonavenue.com', None, 'http://crurestaurant.ca', 'http://www.arizonapaintingcompany.com/', None, 'http://www.equityapartments.com/Arizona/Phoenix-apartments/Scottsdale/San-Marcos-apartments.aspx', '1592229547', 'http://www.calakmulaz.com', 'http://www.pamperedpoocheslasvegas.com', None, 'http://torontovintage.ca', 'http://www.preservationcleaning.ca', 'https://www.homedepot.com/l/West-Aurora/IL/Aurora/60506/1957?cm_mmc=seo-yelp&', None, None, 'http://www.glowbeautycharlotte.com', 'http://www.attorneyramsey.com', None, None, None, 'http://www.kjsdental.net', '1592229581', 'http://www.buchanans.ca', None, 'http://www.khaanakhazanaaz.com/', None, 'https://www.torrid.com/store-details?StoreID=3512', 'http://www.croatiarestaurant.ca/', 'http://kblossomshop.com', 'http://www.phoenixlosburritos.com', 'http://drorona.com/', None, None, 'https://www.signaturestyle.com/locations/wi/madison/cost-cutters-maple-grove-shopping-center-haircuts-16214.html', None, None, 'http://www.mountainpark.org', 'http://www.alamo.com/', 'http://sweettomatoes.com', 'https://nixrockstargarage.com', 'http://glownailbarhenderson.com', 'http://www.heartbreakersalon.ca', 'http://lahmajounsevan.com/', 'http://www.tapino.com', 'http://www.hotdogonastick.com', None, 'http://www.ScruffyToFluffyLV.com', 'http://www.sagamorehillsanimalhospital.com', '1592229642', None, 'https://www.wellsfargo.com', 'http://www.balzermotorworks.com', None, 'http://www.pdqstores.com/gmaps/Wisconsin/MadisonArea/131.html', 'http://www.meadows-chiro.com', 'http://www.levinfurniture.com/furniture-store/pa/pittsburgh/5846-forbes-ave', None, 'http://www.futurekiddie.com', None, None, None, None, 'http://www.starbucks.com', None, '1592229673', 'http://southpointcasino.com/landing?cid=ypsp', None, 'http://www.shigatsusushi.com', 'http://lasvegasballroomdancing.com', None, None, 'http://www.brakemasters.com', '1592229689', 'http://www.homehardware.ca/en/dealer-microsites/1582-7/contact-information.htm', None, None, None, 'http://www.ascentcle.church', 'https://www.5spice.ca', '1592229702', 'http://www.hairbymegananton.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.charlottepediatricclinic.org', 'http://mastcoffee.ca', 'http://strutbridalsalon.com/', 'https://doctors.bannerhealth.com/provider/Daniel+Arrhenius/776226', 'http://www.bk.com', None, 'http://www.ultralighting.ca', None, 'http://ak-chinpavilion.com', 'http://www.zara.com', 'http://amyhogan.ca', 'http://www.chilis.com/', 'http://www.rainstormcarwash.com', 'http://Moreheadtavern.com', 'http://www.camelbackwomenshealth.com', 'https://az.aaa.com/agent-office-locations/nv/las-vegas/aaa-west-lake-mead-branch', 'https://www.luvasub.com', 'http://www.citysmokeclt.com', None, 'http://www.nailparade.com', 'http://stores.sallybeauty.com/az/mesa/beauty-supply-mesa-az-3292.html', None, 'http://www.Jerksogood.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.accuratecargo.com', 'https://losprimosmeats.com', 'http://www.grottolounge.com', 'https://www.plazaexecutive.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=KL%20execsuite', None, 'http://matthewscarwash.com', 'http://www.bbqislands.net', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://zscreamandbean.com', 'http://www.waxmuseum.net/', 'https://www.dominos.com', None, 'http://www.mccleanerslasvegas.com', 'http://jcls.jazzercise.com/facility/carnegie-jazzercise-center', 'http://duclostoys.com', 'http://www.therightguyshvac.com', 'http://www.thegourmetcave.com', 'http://tremontfarmersmarket.com/', 'http://www.nemdelight.com', None, 'http://www.mohaveeyecenter.com', 'http://www.yumeisushi.ca', None, 'https://www.early-bird.ca', None, '1592229815', 'http://www.pbjpittsburgh.com', 'https://www.starbucks.ca', 'http://clickserve.dartsearch.net/link/click?lid=43700006435129272&ds_s_kwgid=58700000444951114&ds_url_v=2&matchtype=%7Bmatchtype%7D&device=%7Bdevice%7D', 'http://www.conditandassoc.com', None, 'http://www.immortalsinconline.com', 'http://www.butterchickenroti.com', 'http://www.kirklands.com', 'http://www.eatgarbanzoaz.com/', 'http://thevertigogames.com', 'http://www.stadtcafetoronto.com', 'https://locations.waxcenter.com/nc/charlotte/charlotte-arboretum-0169.html', None, 'http://www.privyskincare.com', 'https://www.koekkoekfood.com', 'http://www.burgundysrestaurant.com/', None, 'http://www.usagymaz.com', 'http://www.bodhitreeacupuncture.com', 'http://www.tendertouchmoving.com', 'https://thaiexpress.ca', 'http://www.tenniscabana.com', '1592229868', 'http://www.yogurt-land.com', None, 'http://drivenfix.com', 'http://www.rocknes.com/index.htm', None, 'http://www.econolodge.com/hotel-rock_hill-south_carolina-SC139?source=pmfyelp&pmf=yelp', 'http://www.petco.com', 'http://www.countryinns.com/scottsdaleaz', 'http://www.bigsurffun.com', 'https://studiocpb.mysalononline.com', None, 'http://www.acoresrotisseriechicken.com/', None, 'http://www.oglolas.com', 'https://www.idealimage.com/medspa-locations/pennsylvania/pittsburgh-area/pittsburghwexford', None, 'http://www.bojangles.com', 'http://www.5cinco5.com', 'https://www.indiapalace.ca', 'https://crownpublichouse.com', None, None, 'https://twomaidswexford.com', None, 'http://www.luxdesign.ca', 'https://www.arizonaanimalwellnesscenter.com', 'http://www.clarkcountynv.gov/Depts/parks/Pages/winchester-cultural-center.aspx', 'http://www.renewalbyandersen.com/window-company/720-phoenix-az.aspx/?utm_source=Yelp&utm_medium=localization&mm_campaign=B5863EAA37E0931E94FEB25E4DEEDB54&mm_replace=true&engName=social_Yelp', 'http://www.shopjustice.com', None, None, 'http://www.perfecttimingentertainment.com', 'http://www.bsyhairstudio.com', None, None, 'http://www.welcomepharmacy.ca', 'http://www.friendshipsuites.com/', None, 'https://locator.chase.com/az/cave-creek/28238-n-tatum-blvd', None, '1592229955', 'https://www.panerabread.com/en-us/home.html', '1592229959', 'http://www.crossfitfury.com', 'https://order.qdoba.com', 'http://infinitydentallv.com/', 'http://www.maintenance-pro.com', None, 'https://www.brennansmarket.com', 'http://jetspizza.com', 'http://www.onthegrill.us', 'http://www.myrivertowne.com', 'http://www.plapreschool.com', 'http://www.dpauljewelry.com', None, None, None, 'http://www.forgoodnesscakesaz.com', '1592229997', None, None, 'https://www.eyeglassworld.com/store-list/las-vegas-(s)-nv-89121/', None, 'http://www.swansofinglewood.ca', 'https://www.aqualineplumberselectriciansacrepairphoenixaz.com', 'https://www1.shoppersdrugmart.ca', 'http://www.elirelocation.com', None, None, 'http://www.premiumsweets.ca', 'https://earls.ca/locations/calgary-tin-palace', 'http://www.beadworldinc.com', None, 'http://www.eastsidecannery.com', None, None, 'http://www.pooranivilaas.ca', 'https://www.navyfederal.org/branches-atms/locations/usa/az/phoenix/cmb/', 'http://www.landainails.com', 'https://www.accountingprincipals.com/locations/mesa-az-accounting-staffing-agencies', 'http://tendershawarma.ca', 'http://www.cherryaz.com', 'http://www.theindiegathering.com', None, 'http://www.prontomexicanfood.com', 'http://www.greatclips.com/', 'http://lasvegasrealestatetoday.com', 'http://www.terribleherbst.com/', 'http://freshdelicious.net/', 'http://www.selfconnection.ca', 'https://dealer.sprint.com/experts-choice', 'http://greatlakesbakingcompany.org', None, 'http://www.threedogbakerylkn.com', 'http://www.kiedrowskibakery.com/', None, 'http://www.boernercompany.com', 'https://www.ihop.com/en/restaurants-streetsboro-oh/9700-state-route-14-3606', '1592230084', 'http://pavelsjewelry.com/', 'http://www.suspectvideo.ca', 'http://www.tomasos.com', 'http://www.orenisbetter.com', 'http://az-ent.com', None, None, None, 'http://www.thespottedcouch.com', None, 'https://giorgio.ca/fr/restaurants/succursale/laval/', None, 'http://chiropractorpeoriaaz.com', None, 'http://www.gandgmarine.com', 'http://www.azdot.gov/mvd/', 'http://reeis.com', None, 'http://www.cuffsclothing.com', 'http://www.candomoving.com', 'http://www.cappysonwalnut.com', None, None, 'http://baraongles.ca', 'http://www.ellenmerkinod.com/', 'http://www.lynnbuss.com?cmpid=lvji_blm_0006', 'https://www.unitypoint.org/madison/home-health.aspx', None, None, 'https://www.ditkasrestaurants.com/Locations/Wexford', 'http://embassysuites3.hilton.com/en/hotels/pennsylvania/embassy-suites-by-hilton-pittsburgh-international-airport-PITATES/index.html', '1592230150', 'http://greenvalley.schoolofrock.com/?labelSource=Yelp&utm_campaign=yelp&utm_source=yelp&utm_medium=yelp&utm_content=yelp', None, 'http://www.lamexicana.ca', 'http://www.mymexquite.com', None, None, 'http://www.bayti.ca', None, 'http://www.rhythmcatsshow.com', None, 'http://bcpoolsupply.com', 'http://www.besolasvegas.com/', 'http://www.allclimatenc.com', 'https://www.wellsfargo.com/locator/bank/32__CATAWBA__ST_BELMONT_NC_28012/', 'http://www.innzonerainbow.com', 'http://www.airparkbike.com/', 'http://www.tolmtaz.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/3825+Monticello+Boulevard-Cleveland+Heights-OH-44121/storeid=3337?cid=ps_ylp_2020', 'http://www.breathinghands.com', 'http://www.tropicalsmoothiecafe.com', 'http://phoenixnap.com/', 'http://www.canadel.ca', None, 'http://www.rogerkdowney.com/?cmpid=rkr3_blm_0006', 'http://www.caldensebakery.ca/', None, 'http://www.cegdealers.com', 'http://www.toysrus.ca', None, None, None, None, None, 'http://www.lvprestigecleaning.com', None, 'http://www.chtoyota.com', 'https://www.petersendean.com/?utm_source=yelp&utm_medium=referral', 'https://locations.waxcenter.com/pa/mccandless/mccandless-0287.html', 'http://www.turcopersian.com', 'http://www.haji-baba-tempe.com/Haji-Baba.com', None, None, 'http://www.jojosmenu.com', 'http://www.proficientclean.com', None, 'https://www.popeyes.com/store-locator/store/restaurant_82776', 'https://www.mattressfirm.com', 'http://www.snohc.com', 'http://www.napaautopro.com/auto-repair/alberta/calgary-renfrew-auto-service/', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://www.ezpawn.com/locations/nv/henderson/10075-eastern', None, 'http://www.ultimatecrc.com', 'http://www.camelbackcab.com/', 'https://www.duluthtrading.com/locations/?city=Belleville&StoreID=004&street-address=1107RiverSt.', 'http://www.chandlersmiles.com', '1592230275', 'https://www.forever21.com', None, None, None, 'http://www.nextcare.com/locations/az/98th/?utm_sourceYelp&utm_mediumLocal&utm_campaign98th', None, None, 'https://www.mattressfirm.com', 'http://www.gianteagle.com', None, 'http://www.boltonpizzapanini.ca', 'http://dms.netmng.com/si/cm/tracking/DGTrackingRedirect.aspx?siclientid=2918&siredirect=http%3a%2f%2fwww.extendedstayamerica.com%2fhotels%2foh%2fakron%2fcopley-east&sisearchengine=1524&siproduct=2557_Bus', None, 'http://www.thanglong.ca', 'http://azfamilydentistry.com', 'http://www.deltaco.com', 'http://www.awakennutrition.com', 'http://www.alphasdiscoveryclub.com/indoorplayground', '1592230318', 'http://www.flourandbarley.com', None, 'http://www.nevadacareerinstitute.com', None, 'https://www.enterprise.com/en/car-rental/locations/us/az/fountain-hills-5029.html?mcid=iyp:8368400', 'http://sonedental.com', 'http://www.get-go.com/storelocator/storedetails.aspx?storeid=294', None, 'https://www.goodyearautoservice.com/en-US/shop/AZ/Goodyear/000908232-85338-1430', None, 'http://www.atlasespressobar.com', 'http://www.foothillsrehab.com/', None, 'http://www.aliveandfreehypnosis.com', None, 'http://www.pizzaiolo.ca/?utm_source=Yelp', None, 'http://floorshop.ca', None, 'http://www.southcharlotteanimalhospital.com', None, 'http://www.morfurniture.com', 'http://www.royalpgh.com', 'http://navarautoandtire.com', 'https://www.jerseymikes.com/8009', '1592230379', 'https://www.hilton.com/en/hotels/clehtht-home2-suites-cleveland-beachwood/?SEO_id=YELP-HT-CLEHTHT', 'http://www.kay.com', '1592230386', 'https://www.davidcreechmd.com', 'http://www.rabbatphoto.com', 'http://eddysautoservice.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYZOT', 'http://www.estrestaurant.ca', 'https://www.180automotive.com', 'http://www.proaquatic.ca/', 'http://www.fastbiryani.com', None, 'http://asairoofing.com', 'http://www.lightrx.com/arrowhead', None, 'http://demetres.com', 'http://www.cre8iveevents.com/', 'https://www.4patientcare.ws/wsv3pro/web/webschedulerv3.aspx?SessionID=2050212', 'https://www.bcautospecialists.com/index.php', 'http://www.JimmyJohns.com', 'http://www.stonetheatres.com/#/sun-valley-14/4579599036', 'https://canyonstateac.com', 'http://www.inexcreativefloors.com', 'http://www.hotelvalleyho.com/vh-spa', None, 'http://www.rhodesranchgolf.com', 'https://www.isluxury.com', 'http://www.yogastyles.com', 'https://pho-oc-vietnamese-restaurant.business.site', None, None, 'http://www.arrowheadoralsurgery.com', '1592230459', 'http://www.fnfcarpetcleaning.com', None, None, 'http://www.slashsalon.com/', 'https://www.mgmresorts.com/en/hotels/united-states/mgm-northfield-park.html', 'http://musa-restaurant.business.site', '1592230477', 'http://www.wellsfargo.com', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://gourmetgringos.com', 'http://www.enlivant.com/communities/arizona/kingswood-place-surprise/?utm_campaign=local&utm_medium=Y&utm_source=listings', 'http://www.tiltedkilt.com/', 'http://www.azskindoc.com', 'https://www.tranquilwatersmedspa.com', 'http://www.KulturaToronto.com', None, 'http://www.kristinachartier.com', '1592230508', 'https://www.theprosperitygoddess.com', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FCLTCG', 'http://www.walmart.ca/en/walmart-meadowvale-supercentre/3054', 'http://www.harlemglobetrotters.com/', 'http://www.affordableappliancerepair.net', 'http://phoenixchildrens.org?utm_medium=local-listing&utm_source=chatmeter', None, None, 'http://www.avenuetaphouse.com', 'http://www.torrid.com', 'https://whiteoakanimalsafehaven.com', None, 'http://www.campusdish.com/en-US/CSW/UNLV', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.boomerangpilates.ca', 'http://www.lvsubzero.net', 'http://genghisgrill.com', 'http://www.pinkhouseboutique.com', 'http://www.sdmattress.com', 'http://www.prairiewindsvet.ca', None, None, None, None, 'https://www.pteglv.com/locations/pts-gold/st-rose-eastern/', None, 'http://theloftmedspa.healthcare', None, 'http://gottabegarys.com', None, 'http://www.thebiddlelawfirm.com', None, '1592230586', None, 'http://www.cookiesbygeorge.com', None, 'http://aquinolawgroup.com', 'http://skinnywimpmoving.com', 'http://locations.whichwich.com/AZ/Tempe/Tempe-Gateway', 'http://clevelandfurniturebank.org', 'http://thedizzy.ca/', 'http://www.libertyclinic.com', 'http://www.windowtreatmentslasvegasnv.com', None, 'http://www.portofsubs.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', 'http://www.familydollar.com', 'https://visionsource-studio-2020.com', 'https://locations.traderjoes.com/az/tempe/93/', None, 'https://www.galleryhiart.com', 'http://dyslexiacenter.com', 'http://www.latinmasstimes.com/Nevada/446', None, 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=891&utm_content=bpas', 'http://pipscafe.com', None, None, 'http://www.royaloakdentalcalgary.com', 'https://www.choicehotels.com/arizona/tempe/comfort-inn-hotels/az498/rates', None, None, None, None, 'http://www.aquasealwaterproofing.com', 'http://www.lovinghut.ca', 'http://www.rhinoexterior.com', 'http://store.concept1.ca/store/', 'http://havenhg.com', 'http://WorldsTallestChiropractor.com/', 'http://www.leahs.ca', 'http://thevaporsocial.com/', 'http://www.drpalluck.com', 'http://www.sunsetstation.com/dining/hooters/?utm_source=YELP&utm_medium=SOCIAL&utm_term=SS&utm_content=SS-PROPERTIES&utm_campaign=SS-YELP', 'http://www.newsonganthem.org', 'http://www.rosynails.ca', 'http://www.touchofthai.info', '1592230681', 'http://www.statebicycle.com', 'https://www.bodynbrain.com/scottsdale', 'http://greatscience.com/explore/exhibits/william-g-mather-steamship', 'http://www.arizonacharliesdecatur.com/', 'http://www.trainerjo.ca', 'http://www.myhenrybrown.com/?cs:pro=repman&cs:e=yelp', None, None, 'http://www.g1tour.com', None, 'https://urgentvet.com', 'https://www.mgmgrand.com/en/entertainment/grand-garden-arena.html', 'http://www.blimegreen.com', None, 'http://www.murgatroid.to', 'https://www.segwayofscottsdale.com', 'http://www.iandjfountainrestaurantaz.com', '1592230719', None, None, 'http://www.renegadecoffeeaz.com', None, 'http://www.earnhardtcjd.com', None, 'https://www.target.com/sl/north-olmsted/2016', 'http://schnitzelhub.com/', None, 'http://terramassagepgh.com', 'http://madjackspub.com/', None, None, '1592230745', 'https://www.mountainshadows.com', 'http://www.dukesupperdeck.com', None, 'http://www.qdoba.com/', None, 'https://nevadaeyephysicians.com/Henderson-Office', 'https://www.lebos.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'https://www.jetblue.com', 'http://doughboyspizzaandwings.com/', 'http://www.gordon-law-offices.com', 'http://www.callahans-flooring.com', 'https://madison.floorcoveringsinternational.com', None, None, 'http://www.festivalofcolorsusa.com/festival-of-colors/festival-colors-las-vegas-nv/', 'http://www.gigglingtomatoes.com', 'https://www.dominos.com', 'https://jose-cansecos-showtime-car-wash.business.site', 'http://lvpaiutesmokeshop.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FMSNME', 'https://wholehealthphoenix.com', 'http://www.salondecheveux.com', 'https://www.sportchek.ca/stores/hillcrest-mall.html', 'http://www.thebrooklineplumber.com', 'http://www.arcadiafarmscafe.com', None, None, 'http://lasvegashears.com/audiologist-las-vegas/', 'http://carlitosmokes.com', None, None, 'http://www.mypittsburghlocksmith.com/', 'http://goodwillsp.org/shop/retail-stores/weddington-road', None, 'http://www.magiclaserandaesthetics.com/', None, 'https://www.nextdoorwinebar.ca', 'http://store-locator.barnesandnoble.com/store/2212', None, 'http://www.fallasstores.com', None, None, 'http://www.coopercoons.com', 'http://www.aatexlawn.com', 'https://zacharylawgroup.com', 'https://local.executivecoin.com', 'http://www.azrealsolutions.com', 'http://www.thunderbirdim.com', 'https://www.insynco.com', 'http://www.drstevensabatino.com', None, 'http://www.lasvegasdogtrainers.com/', 'http://progressivedentalandortho.com/', 'https://www.chapmanhyundaiphoenix.com', None, None, 'http://www.a-natural-u.com', 'https://www.redstarvapor.com/stores/vape-shop-gilbert/', 'http://www.hcpnv.com', 'http://www.twtdbooks.com', 'https://www.stylistics.net', None, 'http://www.ashandkris.com', None, 'http://Www.SerenityRichmond.com', None, None, 'http://www.patrickssigns.com', 'http://www.havanacafe-az.com/', 'http://www.mogheltandoori.com', 'http://alpremium.ca/', 'http://www.wincofoods.com', None, None, None, None, None, 'http://www.mygreentreeapts.com', 'http://www.bearcreekaz.com', None, 'https://fixautousa.com/las-vegas-craig', 'http://www.inmotionstores.com', 'http://www.cadencecoffee.com', None, None, 'https://randrpaintingaz.com', 'http://www.labcorp.com', 'http://www.sunautoservice.com/auto-repair/nv/henderson', None, 'http://www.dubinwellness.com', None, 'https://www.alamo.com/en_US/car-rental/locations/location-details/US/PITT71-pittsburgh-international-airport.html?iataNumber=AL022237&affiliateRes=Y&cm_mmc=Yelp-_-IYP-_-National-_-null', 'http://www.pitaland.ca', 'http://www.tuttigelati.com/', 'http://www.burroburrito.com', None, 'http://terravitavet.com/', None, 'https://www.wingilariver.com/index.php/vq-vee-quiva-hotel-casino/dining/fatburger', 'http://imperialexcavatingaz.com', None, 'http://www.bartholomewphotography.com', 'http://lucillemadison.com', None, None, None, 'http://www.starbucks.com/store/9334/', 'http://www.decoraport.ca/francais/', 'http://www.johnnyrockets.com', 'http://boucherville.delfriscos.ca', 'http://beerbatter.ca', 'http://www.quiznos.ca', None, None, None, 'http://withoutwalls.tv/', 'http://Www.kristinlloy.com', 'http://www.letswrap.biz', 'http://www.truevalue.com/hometruevalue', 'http://www.allmetalsrecyclingllc.com', None, 'http://www.jumprestaurant.com/', None, None, 'http://www.chandlercustomcycles.com', None, 'http://www.bwh-services.com', None, 'https://locations.dignityhealth.org/oasis-hospital-phoenix-az', None, 'https://www.smithsfoodanddrug.com/stores/details/706/00370', 'https://locations.panerabread.com/oh/bainbridge-township/8480-east-washington-street.html', None, 'http://www.fred-vincentvw.com/', 'http://www.audreyjanellebeauty.com', None, 'http://www.lauraleesalon.com', 'https://www.bartlett.com/locations/Phoenix-AZ.cfm/?yelp_ads_lop%C3%8A', 'http://appliance-repair-pittsburgh.pa-biz.com', None, 'http://www.starbucks.ca', 'https://sandees-water-n-ice.business.site', None, 'http://www.orvis.com/cleveland', 'http://www.acehardware.com/store-details/06234', 'http://www.fantasticsams.com', None, 'https://www.availvapor.com/north-olmsted', 'http://www.georgiossalonspa.com/', 'http://www.sexyplusclothing.com', '1592231074', None, 'http://eatmegourmetcatering.com', 'http://www.onceuponachildstow.com/', None, None, 'http://www.pianotuneraz.com', 'http://www.framersworkshop.net', None, 'http://www.sunglasshut.com/us/?cvosrc=display.yelp.LasVegas', None, '1592231097', None, None, 'https://www.mandalaybay.com/en/nightlife/rhythm-riffs.html', 'https://www.walmart.com/store/4356/las-vegas-nv/details', 'http://www.bosmeadery.com/', 'https://www.steaknshake.com', None, 'http://www.dolcelucano.com/', None, 'http://storelocator.pepboys.com/pepboys/stores/phoenix/cactus/00747', 'http://www.jumparoundpartyjumpers.com', 'http://www.NextLevelTreeLLC.com', None, 'http://www.jimmyscoffee.ca', 'http://www.bigotires.com/regions/Nevada', None, 'http://www.onegooddoctor.com', 'https://www.aqualityelectric.com', 'http://www.actionappliancepitt.com', 'http://www.fetishfalls.com', None, 'https://www.camdenliving.com/scottsdale-az-apartments/camden-foothills?cm_mmc=Yelp', None, 'http://www.themilkshakefactory.com', 'http://www.opalasvegas.com/', None, 'http://relaxologywellness.com', 'http://www.greatclips.com/', 'http://l.macys.com/biltmore-fashion-park-in-phoenix-az?cm_mmc=Yelp_Stores-_-Phoenix-_-n-_-451&m_sc=sem&m_sb=yelp&m_tp=text&m_cn=Phoenix_451&m_ac=yelp_stores&m_ag=n', None, None, 'http://hmshost.com', 'http://www.pagoda.com', None, 'http://www.2fixmyair.com', 'http://lazioitalianbakery.com/', 'https://www.flyfrontier.com', 'http://warraichmeats.com/', 'http://bhelwalaindianfood.com/', 'https://www.enterprise.com/en/car-rental/locations/us/nv/north-las-vegas-craig-rd-5404.html?mcid=iyp:8368400', None, None, None, 'https://azvent.com/locations/estrella.php', None, None, 'http://www.ahealershand.com/', None, 'http://www.thedelevagroup.com', '1592231200', None, None, 'http://www.libertywildlife.org/', None, None, 'https://www.emilianos.net', None, 'http://www.klassynailscalgary.com', 'https://stores.cortfurnitureoutlet.com/arizona/chandler/150-south-kyrene-suite-1/?utm_source=yelp&utm_medium=organic&utm_campaign=localmaps', 'http://www.pintoranch.com', None, 'https://locations.timhortons.com/ca/on/markham/5000-hwy-7-e.html', 'http://www.institutefordriverssafety.org/', None, 'http://allautobattery2007.com', 'http://www.paulstailors.com/', None, None, 'http://www.purplesagesalon.com', 'http://www.rockwoodnaturalmedicine.com/', None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'https://www.westelm.com', 'http://robertostacoshop.com', None, 'http://www.banfield.com/veterinarians/nc/charlotte/bky?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89015/601-in-henderson/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-601&utm_content=website-link&howheard=IYE', 'http://banditolv.com', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=352&utm_content=bpas', 'http://www.bigotires.com/regions/Nevada', 'https://www.appletreedentalforkids.com', 'http://www.lizzynco.com', 'http://www.skylarparkeraz.com', None, 'http://www.btvape.com', 'http://www.tenrestaurantaz.com', 'http://www.zoestrunk.com', None, 'https://www.popalock.com', 'http://www.zaborfh.com', 'https://www.sunamg.com', None, 'https://www.awomanschoiceinc.com', 'https://www.walmart.com/store/2720/madison-ms/whats-new', 'http://www.cannonschophouse.com', 'http://www.school-for-massage.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216494&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', None, 'http://www.aquariuslandscapinglasvegas.net', None, 'http://www.snowdentistry.com', None, 'http://www.westhillsnissan.com', 'http://www.marcos.com/', 'http://bermanchiro.net', None, 'http://www.lcbo.com/lcbo-ear/jsp/storeinfo.jsp?STORE=629&language=EN', 'http://www.myazsmile.com', 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89148/591-near-spring-valley/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-591&utm_content=website-link&howheard=IYE', None, '1592231336', None, None, 'http://agentpestcontrol.com', 'http://www.gilleyslasvegas.com', 'http://www.drsmarkantone.com', 'http://www.dollarama.com', 'http://www.vbsconstruction.com', 'https://locations.wendys.com/canada/ab/calgary/7109-macleod-trail-s-w', 'http://www.rockruninn.com', 'http://www.jamburritos.com', 'http://www.icenowaz.com', 'http://www.thebarrelinn.com', 'http://www.pierdeorleans.com', None, 'http://www.transitionsquad.com/', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.hennashoppe.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'http://www.buffalophoto.net', 'http://www.skyzone.com/ca/mississauga', 'https://www.destinationhotels.com/tempe-mission-palms/dining/tempe-restaurants', 'http://www.summitfamilydentist.com', 'http://www.notoriousautodesigns.com', 'https://www.wellsfargo.com', 'http://www.walmart.com/', '1592231397', 'https://centralusa.salvationarmy.org/danecounty', 'http://www.thetheodore.beer', 'http://www.michaelruffattodmd.com', 'http://www.quiktrip.com', 'http://www.metropolis-living.com/', 'http://www.buildabear.com?sc_cid=ds:yelp:profile', None, '1592231415', 'http://lagourmandinebakery.com', 'https://www.artclassesforkids.com', None, 'https://www.coulternissan.com', 'http://www.harborfreight.com', 'http://www.loveandcaresitters.com/', 'http://scottsdaleprinting.org', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.wallacefloral.com', 'http://kellyclark.com', 'http://www.papa-luigi.com', None, 'https://www.wellsfargo.com', 'https://nativegrillandwings.com/location/pebble-creek/?utm_source=Yelp&utm_medium=Local&utm_campaign=Pebble_Creek', 'http://www.skinnydippingpools.com', 'http://www.kfc.com', '1592231454', 'https://eyetique.com/squirrel-hill', None, None, 'http://www.bargainballoons.ca', 'http://www.sonicdrivein.com/', 'https://www.erbertandgerberts.com/locations/?store_address=53703', 'http://www.papagnos.com', None, 'http://www.johnnymcguires.com/vegas/', 'http://www.beaumontalignment.com', None, 'https://www.dapperandstout.com', 'http://www.uhhospitals.org/north-olmsted/urgent-care', 'https://www.barnettfalls.com', None, 'http://www.greatdanepub.com/', 'http://www.skodagordon.com', 'http://www.raffmobilemechanic.com', '1592231495', None, 'http://www.maac.com/south-carolina/columbia/the-fairways?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'https://www.walgreens.com/locator/walgreens-8816+e+pinnacle+peak+rd-scottsdale-az-85255/id=3602', None, 'http://www.dannburg.com', None, None, None, 'http://routes.ca', 'https://locations.tiaa.org/nc/charlotte/8500-andrew-carnegie-blvd?tc_mcid=bn_yelplocal_0618', 'http://sweetpeacafe.moonfruit.com/', 'http://www.EveryKidsDentist.com/?sc_cid=Yelp_Listing', 'http://www.healthyplanetcanada.com/stores/index/view/store/13', None, 'https://squarefeat.com', 'http://www.advancedtherapeutics.ca', 'http://www.eighteeneight.com/beachwood-oh', '1592231531', 'https://www.moes.com/find-a-moes/pennsylvania/wexford/100189?utm_source=yelp&utm_campaign=yelp&utm_medium=referral', None, 'http://www.arizonabestmaids.com', None, 'http://www.amournailsandspa.com', None, None, 'https://www.hilton.com/en/hotels/phxgthx-hampton-suites-phoenix-gilbert/?SEO_id=YELP-HP-PHXGTHX', 'https://www.cooperfamilydentistryaz.com', None, 'http://www.hendersonchevrolet.com', 'http://www.dentalassistingaz.com', 'http://www.senecacollege.ca', None, 'http://philthyphillys.com', 'https://www.kaltire.com/en/stores/locations/?StoreID=694&source=yelp_track', 'https://www.restoration1ofgreaterlasvegas.com', None, 'http://www.arizonalasik.com/', 'http://www.downtownhomeinn.com', 'https://stores.petco.com/pa/pittsburgh/pet-supplies-pittsburgh-pa-1812.html', 'https://www.saigeboutiquesalon.com', 'https://barbaraannsalterations.com', 'http://www.vivitaspa.com', None, 'http://footreflexologychandlergilbertaz.com/', 'http://www.rycoplumbing.com', 'https://www.petpeoplestores.com/strongsville-store.html', 'http://www.paulsacehardware.com', None, '1592231602', 'http://www.thegrubclub.com/a/daddydukes', 'http://mesaunderground.com/', 'https://refinedlightingaz.com', 'http://www.thechildbirtheducator.com', None, None, None, None, 'http://www.desertstorage.com/scottsdale-az-storage-units', None, 'http://www.petiterestaurant.ca', None, None, '1592231633', 'http://www.falcononeclt.com', 'http://www.fracascleveland.com/', 'https://stores.arhaus.com/oh/akron/2246-west-market-street.html', 'https://www.publicstorage.com/north-carolina/self-storage-charlotte-nc/28210-self-storage/1196?pid=wyelp&CID=1245&CHID=AFL', 'https://www.lolplay.ca', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=101', 'http://www.somethingnewmedia.com', 'http://www.mughaircuts.com/', 'http://www.pcmloan.com', None, None, 'http://sanfrancescos.com', 'https://www.thephoenician.com/phoenician-tavern/', 'http://www.aeopowersports.com', 'https://www.redlobster.com/locations/list/az/peoria/7921-west-bell-rd', 'http://locations.arbys.com/us/nv/north-las-vegas/1465-w-craig-rd.html', None, 'http://www.usps.com/', 'https://az.aaa.com/agent-office-locations/az/phoenix/aaa-paradise-valley-auto-repair', None, 'http://www.ellamentssalon.com', 'https://shuyi.ca', 'http://www.macxn.com/stores/madison-wisconsin', 'http://pedispanailbar.com', 'http://www.vaudreuilvolkswagen.com', 'https://www.anytimefitness.com/gyms/2160/Scottsdale-AZ-85266/?utm_source=yelp&utm_medium=local', 'http://www.mcdonalds.com', 'http://www.patriotmovers.us', 'http://www.furnitureappliancemart.com/current/Stores/Madison_West_Wisconsin_Furniture_Store.aspx', '1592231701', 'http://www.yorkvilleespressobar.com', None, 'http://www.italianvillagepizza.com/', None, None, None, 'http://www.rossstores.com', None, 'http://www.honeycombedhair.com', None, None, 'http://frostyvalleygolf.com/', 'http://www.builderzwarehouse.com', 'https://www.callawayirrigation.com', 'http://www.Boothbuilt.com', 'https://www.lalasercenter.com/centennial/?utm_source=yelp&utm_medium=centennial&utm_campaign=centennial%20dermatology%20and%20laser%20cancer', None, None, 'https://www.idealimage.com/medspa-locations/nevada/las-vegas-nv-area/lasvegassummerlin', 'http://www.epoxyfloorsphx.com', None, 'http://www.bmdprinting.com', 'http://www.warfieldhairbar.com', 'http://www.jandsautoservice.com', 'http://link.hertz.com/link.html?id=46190&LinkType=HZLK&TargetType=Homepage', 'http://Ljhaircuts.com', 'https://www.caesars.com/flamingo-las-vegas?utm_campaign=Yelp&utm_source=yelp&utm_medium=local&utm_term=FlamingoLasVegas&utm_content=hotel', 'http://www.bitsandbytesllc.com', 'http://www.timhortons.com/', 'https://stores.dickssportinggoods.com/nv/las-vegas/1266/', 'https://www.checkcity.com/locations/nevada/lake-mead-and-torrey-pines/', 'https://www.zerorezmadison.com', 'http://www.sheppardvillagedental.com', None, 'http://www.avenue.com', '1592231786', None, '1592231790', 'https://www.camdenliving.com/tempe-az-apartments/camden-tempe', None, 'http://www.qdoba.com/', None, None, 'http://www.pizzahut.ca/', 'http://www.cafelabella.com/', None, 'http://www.agassiprep.net', 'http://www.scarlettplus.com', 'https://gilberteast.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.planetfitness.com/gyms/madison-west-broadway-wi-797?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://lisnoodles.com', 'http://idealcustomflooring.net', '1592231823', 'http://www.picanhalv.com', None, None, 'http://elpalenqueeastlake.com', None, None, 'http://universitycoinandjewelry.com', 'http://www.rajskitchennc.com', 'http://www.strongsvilleheating.com', None, 'http://www.thebutcherspantry.com', 'https://locations.dignityhealth.org/emergency-room-at-arizona-general-hospital-glendale', 'http://www.artisticalloys.com/', 'http://www.silkmedspa.ca/', 'http://www.arizonalodgingexperts.com/owner-support/scottsdale-az-property-management/', 'http://allntattoo.com', 'http://www.belleetboeuf.com', 'http://www.spice9cuisine.com', 'http://lensfactory.ca', 'http://www.mark-taylor.com/arizona/stone-oaks/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'https://www.aldoshoes.com/ca/en', 'http://www.shopartmart.com', 'http://www.womeninneed.net/', 'https://www.atozdiscountdepot.com', 'http://lifetimegaragedoorsaz.com', 'https://www.alphaandomegadogtraining.com', 'http://ajustbrewcoffee.org', 'https://www.brooklynbedding.com/showrooms/arizona/phoenix-buckeye/?utm_source=yelp.com&utm_medium=referral&utm_campaign=yelppage', 'http://www.yellowjersey.org/', None, None, 'http://www.cafelouise.ca', None, None, 'http://www.izzazu.com', 'http://www.posterjack.ca', 'https://local.firestonecompleteautocare.com/nevada/las-vegas/3770-s-maryland-parkway/', 'http://orangeleafyogurt.com/frozen-yogurt-store/OH/gates-mills-/6679-wilson-mills-rd?id=384', 'http://www.zaidmoving.com', 'http://www.exoticnailstouch.com/', 'http://www.cartelbrewery.com', 'http://www.greasemonkeyhuntersville958.com', 'http://dresslersrestaurant.com', 'http://superdupermovers.ca', 'http://aquasportscuba.com', 'http://mortlandpt.com/', 'http://www.firstimpressionnails.ca', 'http://www.coffeepubs.ca', 'http://www.empirebagels.com/', None, None, 'http://www.mcramyun.com', 'http://www.ledesmafootandankle.com', 'https://www.bobevans.com/our-restaurants/locations/146?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'https://www.papillon.com/las-vegas-tours/?utm_source=yelp&utm_medium=cpc&utm_campaign=papillon-las-vegas', 'http://www.bytesbackdatarecovery.com', 'https://www.macu.com/Branch-Locations/AZ/Mesa/Mesa-Branch/0033', None, None, None, None, 'https://www.regmovies.com/theatres/regal-manor-twin/1841?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Manor+Twin', None, 'http://www.barneys.com/location#!/stores/14', 'http://www.getenergysmarter.org', 'http://hooterscasinohotel.com', None, None, None, None, 'http://www.dianasseafood.com', 'http://www.theloadeddog.ca/', 'https://www.restaurantszibo.com/les-restos/boisbriand', 'https://www.prolinkprotection.com', None, 'http://www.hairhappiness.com', None, 'https://www.playfalcongolf.com', 'http://www.cpracademylv.com', 'http://www.quiktrip.com', 'http://www.kennelcarevet.com', None, 'http://www.athletico.com/locations/urbana/', 'https://www.sgtclean.com', 'http://brucehalllaw.com', 'http://www.westernskiesgolf.com/', 'http://homewoodsuites3.hilton.com/en/hotels/ontario/homewood-suites-by-hilton-toronto-mississauga-YTOHWHW/index.html?SEO_id=YELP-HW-YTOHWHW', None, 'https://www.medicentres.com/chiropractic/', None, '1592232037', 'http://home.vivoli.ca/', 'http://www.ncdentist.com', None, 'http://www.poetryjazzcafe.com/', 'https://locations.tropicalsmoothiecafe.com/nv/henderson/10612-south-eastern-avenue', 'http://www.malleys.com', None, 'http://www.junk-works.ca/locations/toronto-north', None, None, 'https://www.frontieraptmovers.com', 'https://www.hattendo.ca', None, 'http://www.housecallnotary.ca', 'http://bunsofsteelbootcamp.com/', '1592232072', None, 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=118&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-118', 'http://thekeyrealtyteamaz.com', 'http://www.arcadiachiro.com', None, 'https://www.180smoke.ca/vape-shop-etobicoke-islington-electronic-cigarettes', None, 'http://www.soulpepper.ca/', None, 'http://www.autotruckandfleetservices.com', 'http://hiltongardeninn3.hilton.com/en/hotels/north-carolina/hilton-garden-inn-charlotte-concord-CLTCOGI/index.html?SEO_id=YELP-GI-CLTCOGI', 'http://igniteperformance.net', 'http://www.smartbookingtravel.com/', None, 'http://www.sashandbustle.com/', 'http://www.bestratemtg.com', 'http://hibachisan.com/', None, None, 'http://www.acneadvisors.com', None, None, 'https://www.classictan.biz', 'http://www.cityofhenderson.com/henderson-happenings/parks-and-trails/locations-and-features/reunion-trails-park-and-amargosa-trailhead', 'http://juicdlife.com', '1592232129', 'http://www.tutortime.com/your-local-school/phoenix-az-6086/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', 'http://www.letstalktherapy.com', 'http://www.downtownerlv.com', 'http://www.melrosekitchenaz.com', 'http://www.somethinsweet.ca', None, None, 'http://www.climateprollc.com/', 'http://Www.artistichandsmassage.com', 'https://locator.chase.com/az/scottsdale/15415-n-65th-pl', 'http://www.scottsdaleeyesurgerycenter.com', 'https://www.brewerairporttoyota.com', 'http://springfieldgolfresort.com/', None, 'http://www.bodyworkscentral.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.elpasobarbeque.com/', None, 'http://www.mitchiesmunchies.com', 'http://www.jardinalex.com/?srccode=yelp_track', 'http://www.homesmartinternational.com', 'https://mkbjj.com', 'http://www.outside-inspirations.com', 'http://www.mayereyecarelv.com', 'https://kimmynailsandspa.weebly.com', 'http://www.tree-removal-phoenix.com', None, None, 'http://www.e-mg.com', 'http://www.amayaexpress.com/', None, 'http://www.winners.ca', None, 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FLASGR', '1592232211', 'https://www.loblaws.ca/store-locator/Glen+Erin+Drive%2C+Mississauga/1011?storeId=1011', 'http://www.tamalerialaurita.com', None, '1592232222', None, 'http://www.CharlotteHealthCenter.com', 'http://www.ihg.com/intercontinental/hotels/gb/en/cleveland/clehb/hoteldetail', 'http://www.rockymountaintails.ca', None, 'http://www.meineke.com', 'http://www.semprepizzapasta.com', 'http://symposiumcafe.com/woodbridgerestaurants.html', None, 'https://elementsmassage.com/Phoenix-Arcadia', 'https://graylinelasvegas.com', '1592232247', None, None, 'http://iwearthebest.com', 'http://www.repeteslv.com', 'http://www.managestaff.com', None, 'http://www.urbanpalm.com', 'http://www.livelifeblended.com', 'http://www.empire.edu/cosmetology-schools/north-carolina/charlotte-pineville', None, 'https://rightspacestorage.com/self-storage-locations/nevada/las-vegas-nv-storage-units/3043-N-Pecos-Rd/', None, 'http://www.phxortho.com', None, 'http://www.petvalu.com', 'http://hummusfactorylv.com', None, None, 'http://www.pelicanssnoballs.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/4755+West+Ann+Road-North+Las+Vegas-NV-89031/storeid=2989?cid=ps_ylp_2020', 'http://nvpicapart.com', 'http://www.mrosmow.com/', 'http://www.lofgreens.com/', None, 'https://rtcatcafe.org', 'https://www.surpriserental.com', 'http://tjmaxx.tjx.com/store/stores/storeLocator.jsp?_requestid=62549', 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6006', 'http://www.btbouncies.com', 'http://www.tinnenfamilychiropractic.com', 'http://www.blushlane.com', 'http://archwaychandler.greatheartsacademies.org', None, None, 'http://www.grillies.ca', None, 'http://www.backcarechiropractic.com', 'https://www.mypetmarket.com', 'http://www.visionworks.com', None, None, 'https://www.anytimefitness.com/gyms/288/Las-Vegas-NV-89139/?utm_source=yelp&utm_medium=local', 'http://www.happyhauscleaning.com', None, 'http://www.steaknshake.com/locations/23949-steak-n-shake-cherry-road-rock-hill', 'http://www.irepex.com', 'http://glutenfreegoat.com', 'http://www.rossstores.com', 'http://www.dogdayslasvegas.com', None, 'https://www.allvalleycarcare.com', 'http://www.thepigeonguy.com', None, 'http://www.etchsalon.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.sugarfactory.com/', 'http://clickserve.dartsearch.net/link/click?lid=43700044281357789&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'https://locations.jackinthebox.com/us/az/phoenix/620-e-buckeye-rd', None, 'http://quicksmiles.com', 'http://www.southbrookpumpkins.com', 'http://www.starbucks.com/store/9298/', None, 'http://www.fender.com', 'http://www.arizonaveterinaryoncology.com', None, 'http://chollafamilydentistry.com', 'http://www.aliveprintshop.com', 'http://www.skipro.com', 'https://www.cyclegear.com', 'http://sunriseautosaleslv.com', '1592232418', None, 'http://www.warmspringssurgicalcenter.com', None, 'http://www.safewaytire.net/locations/mode/22/4623-superior-avenue-cleveland-oh-44103.aspx', 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=8248', None, 'http://radioshack.com', None, None, None, 'https://ad.doubleclick.net/ddm/clk/300150600;127077036;j', None, 'http://www.kinospainting.com/', 'http://www.themercurylounge.com', 'http://www.westcanadian.com', None, '1592232457', None, 'http://www.tequilaranchcleveland.com', 'https://www.peaceloveandlittledonuts.com/locations/hudson-oh', 'http://www.azsportscenter.com', 'http://www.UnitedBeautySupply.com', None, 'http://www.phoenixpubliclibrary.org/Locations/Pages/Cholla.aspx', None, 'http://www.chilinoodlecorner.com/', None, 'https://3scocoffeebar.com', 'http://leafandbloom.com', 'https://www.fastmed.com/urgent-care-centers/phoenix-az-walk-in-clinic-maryvale-parkway/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'https://www.homedepot.com/l/Cave-Creek/AZ/Phoenix/85022/480?cm_mmc=seo-yelp&', 'https://www.wyndhamhotels.com/hotel/30821?tel=18882935571&iata=00093785&cid=fe:bh:20161215:yl:pp:hawus:30821', 'http://mcithedoctorsoffice.ca/patients/37-clinic-Mt.-Pleasant', None, None, 'http://www.sabatinospizza.com', '1592232509', 'https://chatters.ca', None, None, 'http://www.greenvalleyrange.com', 'http://www.gangnamasianbbqdining.com', 'http://www.gemini-arcade-palace.com/', 'https://www.mcalistersdeli.com/locations/nc/cornelius/19930-west-catawba-avenue-suite-150-1067', 'http://www.ProOutdoorServices.com', 'http://www.winners.ca', 'http://la-dulce-espera.business.site', 'https://ad.doubleclick.net/ddm/clk/434331165;236814625;c', 'https://cortatefurniture.com', 'http://a519chocolate.com', 'http://gregstruckandautorepairil.com', None, 'http://www.visionsourcewestsahara.com', None, None, 'http://mobileglowaz.com/', 'http://donutparlor.com', 'http://www.greenvalleyobgyn-nv.com', 'http://www.awhitepondparadise.com', 'https://www.circlek.com/store-locator/us/glendale/5848-w-olive-ave/2706657', None, 'http://latinoservices.net', 'https://www.xtendbarre.com/studio/charlotte', 'http://sharpedgebeer.com/index.php/locations/brasserie', 'http://www.cavopgh.com/', 'http://www.ymcaofpittsburgh.org/sampson/', 'http://www.planetfitness.com/gyms/las-vegas-flamingo-nv-611?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', 'http://www.lovesac.com/', 'https://www.samsclub.com/sams/pagedetails/content.jsp?pageName=aboutSams&couponId=YLPADS&PID=YLPADS', None, 'http://thewingfactory.ca', 'https://lmp360media.com', 'http://locations.in-n-out.com/234', 'http://www.Learn2PlayNow.com/', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.JimmyJohns.com', 'http://www.lakeforestcc.org', 'http://www.brittwiththebrush.com', 'http://www.gentlemenscutlakewylie.com/', 'http://www.premierfoliage.com', 'http://www.playacabana.ca/', None, None, 'http://areyoukenilworthy.com/', 'https://www.interstatebatteries.com/locations/all-battery-center-peoria-il', 'https://www.homedepot.com/l/Arrowhead-Ranch/AZ/Glendale/85308/475?cm_mmc=seo-yelp&', None, 'http://www.scottclarknissan.com/?utm_source=yelp&utm_medium=business_url&utm_campaign=local-citations', None, 'http://www.goodlifefitness.com/locations/ontario/northyork/don-millseglinton?source=yelp-websitelink-northyorkdon-gl', 'http://fightertownpaintballpark.com/', '1592232641', 'http://www.barbecuedoctor.com', 'http://www.zinburgeraz.com/locations/gilbert', 'http://www.ifrrealestate.com', 'http://www.botanyflowers.ca', 'http://www.homedepot.com/l/Curity/ON/Toronto/M4B-3L8/7012', 'http://dimurasmoving.com', 'http://www.academyofballroomdance.com', 'https://www.redroof.com/extendedstay/hometownestudios/property/AZ/Phoenix/HTS1059', 'https://mhausnailbar.com', 'http://www.cataldi.ca', 'http://www.thenorvalpancakefactory.com', 'http://www.greenmontvet.com', 'http://realalbertamoving.com', 'https://www.hopewayfoundation.org', None, 'http://www.midas.com/phoenix/store.aspx?shopnum=1241&dmanum=684001', 'http://www.oomomostore.com', 'http://yuphas.com', 'http://lekensington.ca', 'http://us.christianlouboutin.com/ca_en/', 'https://www.redlobster.com/locations/list/il/champaign/1901-n-prospect-ave', None, None, 'http://www.calgaryexpo.com', 'http://www.cheesecakeetc.biz', None, 'http://www.cocktailemporium.com', 'http://west50.ca/', 'http://www.donvalleyendoscopy.com', None, 'https://www.interdent.com/gentle-dental/locations/az/peoria/14155-n-83rd-ave-dentist-office?utm_source=organic&utm_medium=yext', 'http://www.chillinaz.com', 'https://www.oberweis.com/ice-cream-and-dairy-stores/Champaign', 'http://www.orthodoc.aaos.org', None, 'http://www.pregocalgary.com', 'https://www.canadiantire.ca/en/store-details/on/markham-on0.store.html', 'http://www.robstreeremoval.com', 'http://www.sodexousa.com/', 'http://www.tempestlukeshospital.com/', 'https://ikonick.com', '1592232742', 'http://www.yourvacationhome.ca', None, 'http://crockerparkwinefestival.com', 'http://svpsports.ca/stores/steeles', 'http://www.calgarycoop.com/stores/brentwood', 'http://www.papaceo.ca', 'http://www.bulkbarn.ca/en-ca/index.html', 'http://www.alphagraphics.com/centers/tempe-arizona-us004/index.html', 'http://www.floppypawspetsupplies.com', 'http://www.phxsecrets.com', 'http://www.apria.com', 'http://www.onceuponachildscottsdale.com/', 'https://www.belfor.com/en/us/belfor-usa-offices/nevada/las-vegas', None, 'https://www.riteaid.com/store-details?storeNumber=11467', 'http://www.adept.fit', 'http://cibocalgary.com', None, 'http://www.thoseguysmotorcycle.com/', 'https://chadloveservices.com', 'http://phoenixtenniscenter.org', 'http://lagerheads.us', 'http://pizza22ribs.com', 'http://www.funnymagicforkids.com', 'http://barksidebistro.com', '1592232800', 'https://summithomesnv.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B22965780.251857559;dc_trk_aid=448264643;dc_trk_cid=119964345;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', 'http://www.frock.ca', 'http://www.myspace.com/rockyseastside', 'http://www.smgvegas.com', 'http://www.toronto.ca/parks/prd/facilities/complex/467/index.htm', 'http://www.monro.com', 'http://www.wildwingrestaurants.com/franchisees/angus-glen/', 'https://www.goodeyes.com/locations/phoenix/?utm_source=yelp&utm_medium=local&utm_campaign=clinic-phoenix&utm_content=website', 'http://www.einsteinbros.com/', 'http://www.jiffylube.com', 'https://www.moonvalleynurseries.com/locations/northwest-las-vegas?utm_campaign=yelp&utm_source=yelp-nv&utm_medium=rancho', 'https://la-canasta.com', None, 'https://locations.panerabread.com/oh/sheffield-village/5382-abbe-rd.html', '1592232836', 'http://www.frizzhairexp.com', None, None, None, 'https://vespersalon.com', 'http://www.michaelhill.ca/on/demandware.store/Sites-MichaelHillCA-Site/en_CA/Stores-Details?StoreID=148', None, 'http://rudyspub.org', 'http://www.lavishmotoring.com', 'http://www.warehousegroup.ca/el-furniture-warehouse-queen-st', 'http://www.naillacquersalon.com/', 'https://www.benjaminfranklinplumbing.com/las-vegas/', 'https://stores.pepboys.com/nv/las-vegas/506-s-decatur-blvd.html', '1592232869', 'https://www.metropolish17.com', 'http://www.streetsofnewyork.com', None, 'http://www.thepostalroute.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://theritzoflasvegas.com/', 'http://www.greentreehealthandmassage.com', 'http://www.dmvnv.com/', None, None, None, 'http://www.hotelarts.ca', 'http://www.runnymedewalkinmedical.com/', None, None, None, 'http://www.vitalitytap.com', 'http://www.bk.com', None, 'http://sekaisushi.net', 'https://www.frysfood.com/storeHours?store=66000623', None, 'http://ptownbar.com/', 'http://www.limozarizona.com/', 'http://www.lakeshorewellness.ca', 'http://en.hestiatea.com', 'http://www.snapfitness.com/torontohighpark', None, 'http://www.yogapulsestudio.com', 'http://www.veraiconsalonspa.com', '1592232943', None, 'http://www.jaybuickgmc.com', None, 'https://www.menzieschryslerdealer.com', 'http://www.dickblick.com/stores/pennsylvania/pittsburgh/', 'http://www.handandstone.ca/locations/aurora', None, None, 'http://BluBurger.com', 'http://www.nurturedmama.com', 'http://www.cwtow.com', None, 'http://www.fitnesscafemenu.com/', None, 'http://www.vegasmartialarts.com', None, 'http://drtangeyecare.com', 'http://b2burgersbrews.com', 'http://www.copyrite.ca', None, None, 'http://wingardsalon.com/', 'https://hilalgrill.com', None, 'http://www.extremeenergypros.com', 'http://www.ciaobabycatering.com', 'https://baycity-movers.com', None, 'https://www.bannerhealth.com/locations/peoria/banner-urgent-care', None, 'https://www.associated-dental.com/practices/associated-dental-care-chandler', 'https://www.starbucks.ca/store-locator/store/1020633/177-holland-street-east-177-holland-street-east-bradford-on-l-3-z-1-x-8-ca', None, 'http://www.spencersonline.com', None, None, 'http://w.subway.com', 'http://myomedicalmd.com', None, 'http://www.karma.salon', None, None, 'http://powerautobrokers.com/', None, None, 'https://www.ihg.com/holidayinnexpress/hotels/us/en/las-vegas/lasqr/hoteldetail', 'http://robertostacoshop.com', None, 'http://www.allbrightsmile.com', None, 'http://www.publicenemytattoo.net', 'http://www.lucysseacove.com', None, None, 'https://www.nofrills.ca/store-locator/Mario+%26+Selina%27s+nofrills+%28Royal+York+Rd.%29/1371?storeId=1371', None, 'http://beersoftheburgh.com', None, 'http://dnister.ca', 'http://www.wilsonparkerhomes.com', 'http://www.priyashairsalon.com', 'http://www.patoisjamaicanrestaurant.com', 'http://www.thebeautyspotstore.com', 'https://opdaz.com', 'http://www.bearmountainsports.com', 'http://www.foresightchiropractic.com/', 'http://www.palominolv.com/', 'http://www.ralphlauren.com', 'https://wildfire.sclv.com/Barleys?utm_source=Yelp&utm_medium=banner&utm_campaign=yelp-organic', 'http://www.lawrysonline.com/lawrys-primerib/las-vegas', None, None, '1592233109', 'http://www.chnv.org/OurCare/HealthyLivingInstitute.aspx', 'http://www.dunkindonuts.com', 'http://602massage.com', 'http://www.zaffron.ca/', 'http://www.bodyvision.com/arrowhead-studio/', None, 'http://www.hhgregg.com', None, 'https://cityofspice.com', None, 'https://varmintgone.com/locations/varmint-gone-matthews-north-carolina/', 'http://eastlakecanoe.com/', 'http://www.auroraarizona.com', 'http://www.papamurphys.com/', 'http://www.marcstreeservice.com', 'http://www.majesticpalmsapartments.com/', 'http://www.peoplesjewellers.com', None, 'http://www.tempe.gov/city-hall/community-services/community-recreation-centers/diablo-stadium', 'http://stonecreekfurniture.com', 'http://www.centralavenuedental.com', 'https://www.planetfitness.com/gyms/kent-oh?utm_source=yelp&utm_medium=referral&utm_campaign=Yelp_evergreen', '1592233167', 'https://www.atozlandscapinglv.com', None, 'http://www.sundevilauto.com/locations/az/chandler/chandler-22', 'http://www.wickeremporium.ca/', None, 'https://paulmitchell.edu/pittsburgh', 'https://www.chapters.indigo.ca/en-ca/home/storelocator/storeDetails/939', None, '1592233187', 'http://www.rainbowfeatherco.com', None, 'https://www.coca-colacoliseum.com', 'http://www.masterworksautomotive.com/', 'https://www.gianteagle.com/Stores/Store/?storeId=5831', 'https://www.goldfishswimschool.com/wexford/', 'http://www.elcampesinospgh.com', 'http://www.noforksgivenclt.com', None, 'http://www.gokartslasvegas.com', None, None, 'http://www.jacksonlimousines.com', 'http://www.thelashlounge.com/salons/waverly/', None, 'http://www.ACabLV.com', 'https://www.jumagallery.com', 'http://www.suncityawning.com', 'http://www.carrvalleycheese.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'https://www.ashleyfurniturehomestore.com/furniture-stores/united-states/nv/henderson/henderson?cmpid=2016YELP', None, 'http://ratewisemortgage.com', None, None, 'http://www.krispykreme.com', 'https://www.oyorooms.com/76426?utm_campaign=US_PHX004&utm_medium=listing&utm_source=yelp', 'http://www.comda.com/en_ca/', 'https://www.veinscarolina.com', 'http://wedosystems.com', 'https://stores.bestbuy.com/az/avondale/10035-w-mcdowell-rd-1109.html/?loc=ns100&ref=NS', '1592233263', 'http://safransmarket.com', 'http://www.kitchenbathroomremodeling.net', 'http://www.atengarofalodental.com', 'http://diamondnailsofmahomet.com', 'https://www.orangetheory.com/en-us/locations/arizona/surprise/16846-w-bell-rd-suite-106/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.pizzuvio.com', 'http://www.ayrsleynailbar.com', 'https://www.t-mobile.com/store-locator/nv/las-vegas/boulevard-mall-in-line?cmpid=WTR_SE_YXT_U98MLWB9027148', None, 'http://www.sushimaster.ca', 'http://silverstatelocksmith.com', 'https://svdpmadison.org/shop/verona/', None, 'http://www.totalsportsmedicine.com', 'http://www.brazascharlotte.com', 'http://www.nutrition-rush.com/stores.html', 'http://brazilianblowoutsbykatie.com', 'http://www.stammhouserestaurant.com/', 'http://www.eyetecheyes.com', None, 'http://www.girly-girlz.com', None, 'http://www.gatesmillsplace.com', 'https://www.flawlessbyhanna.com', None, 'http://www.sdpetresort.com', 'https://locations.togos.com/ll/US/AZ/Scottsdale/7369-N_-Via-Paseo-Del-Sur*-Ste_-104', 'https://www.aireserv.com/red-mountain', 'http://www.ampm.com', 'http://www.custommedicalmassage.com/pre-and-perinatal.html', 'http://www.nanakcarwash.com', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'https://masteldrycleaning.com/?utm_medium=CTA&utm_source=VYRLYelp', 'http://www.verizonwireless.com/stores/arizona/mesa/val-vista-204086/?INTCMP=INT-LOS-NON-EN-MAKEAPPT-06212015-1LOS1-RE', 'http://www.gotransit.com', 'http://www.geckoshadesolutions.com', 'https://www.blissnailspasc.com', 'https://locations.timhortons.com/ca/on/oakville/494-dundas-st-w.html', None, 'https://locations.massageenvy.com/pennsylvania/bethel-park/5223-library-road.html', 'http://blueiguanapools.com', 'http://www.heirloomsalon.net', None, 'https://www.absolutedental.com/locations/las-vegas/1860-e-charleston-blvd/', 'http://www.kingswayvanlines.com', 'http://www.todaysmenu.ca', 'http://lasvegasnora.com/home.html', None, 'http://www.maac.com/florida/orlando/retreat-at-lake-nona?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://www.7-eleven.com/?yelp=19726', None, 'https://www.lifestorage.com/storage-units/nevada/las-vegas/89015/601-in-henderson/?utm_source=yelp&utm_medium=referral&utm_campaign=YELP-NV-601&utm_content=website-link&howheard=IYE', None, 'https://www.calgarycoop.com/stores/shawnessy/', 'http://www.lawroofing.net', 'http://www.palaisroyale.ca/', 'http://www.blackpeppergrill.com', '1592233399', 'http://www.copps.com', 'http://www.greeningenuity.ca', None, 'https://modellacewigsandhair.com', 'http://www.lebowitzdental.com/', 'http://JamesonAndStaggs.com', 'http://www.atlas-autobodyinc.com/', 'http://www.eyebrowsnatural.com/', 'https://www.miragegm.com', 'https://www.hilton.com/en/hotels/clttohx-hampton-suites-charlotte-ballantyne/?SEO_id=YELP-HP-CLTTOHX', None, 'http://www.designingwomanohio.com', None, 'http://www.southwestjudo.com', 'http://www.healingedgeaz.com', None, None, 'http://stores.fossil.com/az/scottsdale/scottsdale-fashion-square-8304', 'http://www.mrfallstree.com', None, None, None, None, None, None, 'https://www.hilton.com/en/hotels/pitsrhx-hampton-suites-pittsburgh-airport-south-settlers-ridge/?SEO_id=YELP-HP-PITSRHX', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.sweetlanasbridal.com', 'http://www.nakedpizza.biz', None, None, 'http://www.generaltsoskitchen.com/', 'http://www.alteredimage.net', 'http://www.azclar.com', None, 'http://www.songlowboutique.com', '1592233480', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'https://www.excellenceindentistry.com', 'http://www.roofitright.com', 'http://www.3riverslocksmith.com/', 'https://locations.dollartree.com/il/champaign/546/', None, None, None, 'http://www.belllexusnorthscottsdale.com', 'http://www.osbornplace.com', None, 'http://tavernamericana.com/', 'http://www.paybackpest.com', 'http://www.donscigars.com/', 'http://parkinn.com/hotel-torontoca', 'https://www.carolinaasthma.com/location/eastover/', None, 'http://www.lickshomeburgers.com/', None, 'http://www.atsol.com', None, None, None, 'http://oxurban.com', 'http://salonliftohio.com/', 'https://www.cvs.com/minuteclinic/clinic-locator/nc/belmont/2233.html', None, 'http://www.dairyqueen.com', '1592233542', 'http://www.thecarolinadental.com', 'http://www.dentistryofarizona.com', 'http://goodearthcoffeehouse.com', 'http://www.newmarketinn.com/', 'http://www.gilbertperfectskin.com', 'http://www.dermimatch.com', 'https://joeyrestaurants.com/location/joey-crowfoot', 'http://www.health.gov.on.ca/en/public/programs/telehealth/', 'http://www.proarmament.com/index.html', '1592233565', 'http://www.bodricksbbq.com', None, 'http://www.yalebrothers.com', 'http://www.supremeshutters.ca', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://excel-pro-services.com', 'http://www.minpermanentmakeup.com', 'http://www.brainandspineaz.com', None, 'http://www.harmonyvet.com/', 'https://m.costco.com/warehouse-locations/summerlin-las-vegas-nv-685.html', None, 'http://SolisWaverly.com', None, 'http://www.ziggystavernpgh.com', 'http://mustangairmechanical.com', 'https://zestyclean.com', 'https://mvpmodernbarbers.com/bridgeland/', 'http://www.arizonahomeworks.com', None, 'http://www.perfectionistdetailing.com', None, 'http://www.mkt.com/desertrootskitchen', None, 'http://www.rotorooter.com', None, None, None, 'http://www.nafloans.com/', None, 'http://www.ztrip.com', None, 'http://www.umc.org', '1592233641', 'https://www.getgocafe.com/stores/pa/pittsburgh/baum-blvd-getgo/3064', '1592233647', None, '1592233652', 'http://onlyfaces.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=14314', 'http://www.erx247.com', 'http://www.marcos.com/', 'http://www.azextensionsbyjess.com', None, None, 'https://locations.dennys.com/OH/PARMA/247530', None, 'http://www.thaionyonge.com', None, 'http://www.pawstwoclaws.com', '1592233683', 'http://www.reliable.vegas', 'http://www.a1thevacuumshop.com/', 'http://www.zumiez.com', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://www.francisandsonscarwash.com', 'http://arizonapinatas.com', None, 'http://saachispa.com', None, 'http://www.papaprimoz.com', 'http://www.thevoodoolounge.ca/', None, None, 'http://www.themesshall.ca', 'http://goldstarsvc.com', None, 'http://www.neatfreakz@vpweb.com', 'http://www.cityofmadison.com/parks/find-a-park/park.cfm?id=1139', 'http://www.eggspectation.com', 'http://www.yamasushihouse.com', 'https://mylocalmcds.com/willow-pass-concord', 'http://www.tlcpedsaz.com/', None, 'http://www.lvthaimassage.com', 'http://www.frenchconnection.com', 'https://www.giascanvas.com', 'https://affordablebathroomsofaz.com', 'https://www.regmovies.com/theatres/regal-franklin-square/1845?utm_medium=social+network&utm_source=yelp+listing&utm_campaign=Regal+Franklin+Square', None, 'https://www.optumcare.com/state/specialty-care/specialist-locations/rose-parkway-oncology.html', 'http://levetto.com/', None, 'http://www.richlane.ca', 'http://www.pureandsimple.ca', 'http://www.moneyinminutesnv.com', 'http://www.MyMightyMoversAz.com', 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://nathansfamous.com', 'http://www.wvimaging.com/', 'http://www.motimahal.ca', 'http://4lifenaturalfoods.com', 'http://www.uptowncarservice.com', 'http://www.classicmobileairbrushtanning.com', None, 'https://www.walmart.com/store/1464/charlotte-nc/whats-new', 'http://www.medinaoh.org/Parks/Reagan_Park', 'http://westendfood.coop/farmers-market', 'http://www.larichs-pizza.com', None, 'http://aaapws.com', 'http://www.3Brewers.ca', None, 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', None, 'http://blushcleveland.com', None, '1592233815', None, None, None, 'http://northcarolinafertility.com', 'http://www.lasvegascustomloans.com', 'http://www.tacomamaonline.com', None, 'http://www.jacksonswash.com', 'http://perfectpastryonline.com', 'http://www.clevelandexpress.net/index.html', 'http://www.azturfmasters.com', 'http://sidewalkcafeeuclid.com', 'http://mpmvegas.com', 'http://www.streetsofnewyork.com', 'https://www.thejoint.com/arizona/surprise/surprise-48024', 'http://www.playderecord.com', 'http://www.tranquil-bodyworks.massagetherapy.com', 'http://elsombrero.ca/', None, None, 'http://vipbestlasvegaselectrician.com', None, 'http://www.creativedds.com', None, 'http://www.apexendo.com', 'http://senortequilacantinagrill.com/', 'http://abloomsalon.com', 'http://marketcitycaffelasvegas.mypub.website', 'http://www.starbucks.com', 'http://www.quiznos.com/', 'http://www.mesaaz.gov/parksrec/Parks/MountainView.aspx', 'http://www.victoriasfamily.com', None, None, 'https://northtryonlaundromat.com', None, 'http://www.theastrologystore.com/', None, 'http://www.elomsbraiding.com', 'http://www.downtowntorontochiropractor.com', None, None, 'http://www.matthewsfarmersmarket.com/Index.html', 'https://www.wyndhamhotels.com/hotel/52963?tel=18666154223&iata=00093785&cid=fe:lq:20190403:yl:pp:LQUS:52963', 'http://www.secondlookbooks.org', 'http://www.firstqualityroof.com/', None, 'http://www.visionquestbooks.com', None, None, None, None, 'http://www.sallybeauty.com', 'https://www.bowlero.com/location/bowlero-christown?utm_source=yelp&utm_medium=organic&utm_campaign=webclicks', 'http://www.babysbadassburgers.com', 'http://www.phoenixelectricianstoday.com', 'http://www.saulterstreetbrewery.com', None, None, None, 'http://www.labcorp.com', 'https://www.giovannisonline.com', None, None, 'http://www.marbleslab.ca', 'https://www.lush.ca/on/demandware.store/Sites-LushCA-Site/en_CA/Stores-Info?StoreID=129', 'http://www.eatatovereasy.com', 'http://chirotrendz.com/', 'http://www.greenvalleyranchresort.com/dining/china-spice.php?utm_source=YELP&utm_medium=SOCIAL&utm_term=GVR&utm_content=GVR-PROPERTIES&utm_campaign=GVR-YELP', 'http://www.directv.com', 'https://www.gymboreeclasses.com/en/locations/NC/Charlotte/?utm_campaign=Charlotte&utm_medium=website&utm_source=Yelp&utm_content=yelp+page', 'http://brosandbettys.com/', None, 'http://www.lemonfreshcleaning.com', 'http://jetaction.com/', None, None, 'http://www.getitfixed.me', 'http://primozzpizzeria.com', 'http://www.cascadenc.com', 'https://www.fantasticsams.com/about/regions/phoenix-az/fantastic-sams-mesa-az-4', 'http://www.isaute.ca', 'http://www.piesquared.com', 'http://www.thewhitenailsspa.com', 'http://www.bestmassagecenter.com', None, '1592234018', None, 'https://www.brakemasters.com/new-site/stores/1901-n-scottsdale-rd-scottsdale-az/', 'http://happyjoes.com', None, 'http://www.ArrowheadScoopers.com', 'http://www.neatmethod.com', None, 'https://www.usps.com/', 'http://hancockfabrics.com/', 'http://www.albertayogacollege.com', 'http://www.sterling2cleaners.com', 'http://www.royalyorkmeatmarket.com', None, None, None, 'http://signaturenorthwest.com/agent/andrew-lunsford/', 'http://www.madcatpets.com', 'http://www.chasin-tails.ca', 'http://www.roxannesdriedflowers.com', 'https://www.amco-autoglass.com', None, 'http://handymanserviceslasvegasnevada.com', 'http://www.arrowheadnails.com', 'http://www.mcsorleysrestolounge.com/', 'http://www.cityofhenderson.com/parks/parks/sonata_park.php', 'http://www.heartlandpethospital.com', 'http://www.cruisin7th.com', '1592234082', 'http://www.abbotthearingaidcenter.com', 'http://www.townetavernrestaurants.com', None, 'http://www.subvetclinic.net', 'https://stores.jcpenney.com/nv/lasvegas/clothing-stores-lasvegas-nv-2848.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2848', 'http://wendyandersonlaw.com', 'http://www.globalpetfoods.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://nailskathylinhdesign.com/', None, 'http://www.meadowslv.com', 'http://www.ccrfurniturecleaning.com', None, 'https://www.bostonmarket.com/location/university-heights-oh-483/', 'http://www.senecacollege.ca', 'https://www.walmart.ca/en/stores-near-me/markville-mall-supercentre-3053', '1592234121', 'https://www.munichmotorco.com/service-your-car', None, 'http://www.guardianautoglassphoenix.com', 'http://www.thetacobros.com', 'https://www.popeyes.com', 'http://www.impactps.com/', 'http://www.phoenixmentalist.com', 'https://cagiautoglass.com', None, None, 'https://periodontics-dentalimplants.com', 'http://www.nowandthenretro.com', None, None, None, '1592234160', 'http://www.lesportsac.com', 'https://lvsmilecenter.com', None, 'http://www.mysewingroom.ca', 'https://ad.doubleclick.net/ddm/clk/458685338;262921492;w', None, None, 'http://www.shawnessysouthvet.com/', 'http://www.jandbappliance.com', None, None, 'http://www.piscessushi.com', None, 'http://www.techniquerestaurant.com/', 'http://www.scubamagic.biz', None, None, None, None, None, 'https://www.blackmetalfirearms.com', 'https://www.walgreens.com/locator/walgreens-4965+w+bell+rd-glendale-az-85308/id=3049', 'https://locator.chase.com/nv/henderson/637-n-stephanie-st?jp_cmp=rb/LocalListings/aff/branch/na', 'http://www.laalv.com', None, 'http://www.lasvegasswimacademy.com', 'https://www.target.com/sl/waterfront/1253', 'https://www.cloudcarpetonelasvegas.com/about-us/las-vegas', 'http://phoenixcenterforthearts.org/', 'http://www.phoenixknifehouse.com', None, 'http://www.calranch.com', 'http://honeydont.work', None, 'http://www.orobrewing.com', None, 'http://seefuhair.com', 'https://www.petsmart.com/stores/us/az/scottsdale-store0130.html?utm_source=yelp&utm_campaign=us-lcl-srv-eg&utm_medium=listing', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.youngshawaiianstylekitchen.com', 'http://www.brickyardgrounds.ca/', 'http://www.donrandleslawoffice.com/', 'http://johnnyrockets.com', 'https://www.planchatoronto.ca', 'http://www.pawgo.co', None, 'https://www.hertz.com/rentacar/location/unitedstates/northcarolina/charlotte/CLTT12', 'http://www.mtnparkchiropractic.com/', 'http://aquatechplumbingaz.com', None, None, 'http://www.larrygjones.com', 'http://www.myguardianselfstorage.com', '1592234284', None, 'http://www.orleanscasino.com/entertain/bowling?disid=wmm_yelp_to_corporate_bowlingcenter_organiclink', 'http://www.starbucks.com/store/15154/', 'http://www.thefrenchbee.com', None, 'https://finercustomjewelry.com', 'http://colournailssalon.com/', 'http://yummymarket.com/', None, None, 'http://robertostacoshop.com', None, 'http://azpermanentcosmetics.com/', 'http://www.midas.com/toronto/store.aspx?shopnum=9259&dmanum=857001', 'http://www.ocotilloeyecare.com/', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.amerisent.com', 'http://backwards.club', 'https://antikka.ca', 'http://www.turnstyleconsign.com/ahwatukee-phoenix.php', None, None, 'http://www.pjsdayspa.com', '1592234337', 'http://thebrowbomb.com', 'https://www.dunnedwards.com/directory/store-list/summerlin-078', 'http://drscottminer.com', 'https://www.peoriaford.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', None, 'https://www.crashofrhinospainting.com', 'https://www.kohls.com/stores/nv/lasvegas-668.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'http://www.thebakeryphx.com/', 'https://www.usps.com/', None, None, 'http://www.burlingtoncoatfactory.com', 'http://dalesbodyworksllc.com/', 'http://www.petworksco.com', None, 'http://yumyumsofcle.com', 'http://www.thedogdasher.com', 'http://www.hartshornstudios.com/', 'http://europeanpaverssouthwest.com/', None, 'http://www.maleesonmain.com/', 'http://www.equityresidential.com/', 'https://www.publicstorage.com/arizona/self-storage-gilbert-az/85233-self-storage/850?pid=wyelp&CID=1245&CHID=AFL', 'https://www.flavorsoflouisianacajun.com', 'http://www.madbatterbakers.com/', None, 'http://tempefarmersmarket.com/', 'http://www.8bitentertainment.com', 'http://machinodonuts.com', '1592234413', None, 'http://www.westmarine.com', 'https://www.nasm.org', None, None, None, 'https://locations.jackinthebox.com/us/nc/charlotte/7725-pineville-matthews-rd', None, 'https://locations.dennys.com/PA/NEW-KENSINGTON/249565', None, None, None, 'https://www.serviceheroesaz.com', 'http://zabblv.com', None, '1592234448', 'http://www.quiznos.com/', 'http://www.workhorsemarine.com', None, 'http://www.readytorolltire.com', 'https://www.beefjerkyoutlet.com', '1592234462', None, None, '1592234467', None, 'http://christophersfinedrycleaning.ca', None, None, 'http://www.donatos.com', 'http://menu6.org', 'https://www.charlottemeetings.com/charlotte-convention-center', 'http://www.lubestop.com/Locations/Wadsworth', 'http://www.papamurphys.com/', 'http://www.adidas.ca', 'http://www.arizonastoragecenters.com', 'http://www.excelauto.biz', 'http://www.edingersurgicaloptions.com', 'https://www.949atthedistrict.com', None, 'http://www.lvtattoo.com', 'http://www.hobbylobby.com/StoreLocator/Search?Latitude=43.1438143&Longitude=-89.35114950000002&SearchOn=+53704&SearchDistance=25', 'http://www.tacorrito.ca/', 'http://www.pintville.com', '1592234514', None, 'http://www.functionalaestheticdentistry.com', 'http://www.bsjplumbing.com', 'http://www.unitedmessengers.com', 'http://www.kelilabee.com', 'http://www.lovecloudvegas.com', 'http://www.vaco.com', 'http://www.aptfind.com', 'http://www.piesunlimited.com', None, 'http://www.vitalant.org', 'https://locations.usbank.com/index/arizona/tempe/east-elliot-rd-safeway-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', '1592234547', None, 'https://agents.allstate.com/the-bell-agency-henderson-nv.html', None, 'http://www.heroburgers.com', 'http://www.kidsrkidslasvegas.com', 'http://artistichair.studio', None, None, 'https://www.qualtire.com', None, None, '1592234573', 'http://www.animalsupplyhouserockhill.com/', 'http://www.muchoburrito.com', None, 'http://suitenectarsalons.com', 'https://www.filibertos.com', None, 'http://www.truwest.org', 'https://www.dipnailboutiqueocotillo.com', 'http://www.paradisedentalgroup.com', None, 'http://dreamydrawdental.com', 'http://www.mcmurray-manalodental.com', 'http://www.thompsonsautorepair.com', '1592234607', None, None, 'http://www.homewatchcaregivers.com/phoenix', 'http://www.tailgateclothing.com', 'http://www.buybuybaby.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.uwhealth.org/locations/detail.jsp?locationid=124', None, 'https://davidguyettphotography.smugmug.com', 'http://www.midge.ca', None, 'http://mkhouseconsulting.com', 'http://www.torontosculpturegarden.com', None, 'http://EventRents.net', None, 'http://usedcars12.com', 'http://www.azartrestoration.com', 'https://www.circlek.com/store-locator/us/peoria/9476-w-olive-ave/2706468', None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, 'http://waxingaroundtown.com', 'http://www.xtremehomeservicesaz.com', 'http://lasmejorespupusas.weebly.com/', 'http://www.redendos.com', 'http://www.CrowdControlLV.com', 'https://www.kaltire.com/en/stores/locations/?source=yelp_track&StoreID=867', 'http://rickjohn.com', 'http://www.pplusic.com', 'http://www.jabzboxing.com/glendale', None, 'http://www.madisonautodetail.com', 'http://www.fourquet-fourchette.com', 'http://www.dazzlingrestaurant.com', 'http://montereyvetclinic.ca', 'http://www.mrbsfamoussale.com', 'http://www.carserviceoflasvegas.com', 'http://www.suntreehealingarts.com', None, 'http://cirqnightclub.com', 'http://www.ampm.com', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, 'http://www.zabas.com/', 'http://summerwindsnursery.com/az/home?utm_source=yelp&utm_medium=text_link&utm_campaign=website', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=%2Fhotels%2Ftravel%2FYYCWA', 'http://www.santanfamilymedicine.com', 'https://www.circlek.com/store-locator/us/gilbert/888-s-higley-rd/2703373', None, 'https://canyoncreekrestaurant.ca/square-one/', 'http://www.artificialgrassinstallers.com', 'http://www.customcyclerescue.com', 'https://www.usstoragecenters.com/self-storage/nevada/las-vegas/us-storage-centers/135', 'http://www.inland-group.com/location/phoenix/', 'http://www.phxprep.com', 'http://www.DLCphoenix.com', 'http://www.babiesrus.com', 'http://www.ashtangayogalv.com', 'http://upmccancercenters.com/network/upmchillman.cfm', 'https://www.swimco.com/?utm_campaign=Market&utm_source=YELP', None, 'http://www.the-alley.ca', 'https://stores.advanceautoparts.com/pa/murrysville/4010-william-penn-highway?utm_content=listing-2016-12-29&utm_medium=local&utm_campaign=aap&utm_source=yext&utm_term=yelp', None, 'http://www.donalfonsotoronto.com', 'https://locations.jackinthebox.com/us/ca/glendale/1200-w-glenoaks-blvd', 'https://bikeworldlv.com', None, 'http://www.mathnasium.com/litchfieldpark', 'https://haircutmenbocaparklasvegasnv.com', 'http://www.partycity.com', 'http://www.donuttyme.com', '1592234787', '1592234790', None, None, None, '1592234800', None, 'http://www.scottsdaleaz.gov/parks/mountain-view-park', None, 'https://www.gowireless.com/stores/az/fountain-hills/fountain-hills-fountain-hills-plaza/', 'https://www.acesdental.com/areas-served/dentist-north-las-vegas-nv/?utm_campaign=yelpnlasvegas&utm_medium=organic&utm_source=local', 'http://www.rivierahotel.com/las-vegas-entertainment/crazy-girls.aspx', None, 'https://clevelandhomes.com', 'http://www.clipncleandoggrooming.org', None, 'http://www.centurylink.com', 'https://www.chick-fil-a.com/indianland', 'http://www.stabley.net', 'http://www.ledolci.com/', 'http://www.kemptonpt.com', 'http://www.bk.com', 'http://www.schneidersdairy.com', 'http://desertfoothillsgardens.com', 'https://aguayobunch.wixsite.com/a1electric', 'https://www.gianteagle.com/Stores/Store/?storeId=3043', 'http://www.chandlerpediatricdental.com', 'http://www.thereikigal.com', None, 'http://www.slepakinsurance.com?cmpid=RZYD_BLM_0006', None, None, 'http://www.colussy.com/?cs:pro=repman&cs:e=yelp', '1592234868', None, 'http://www.racersedgeperformance.com', 'http://www.waterconnectionaz.com', 'http://www.goindustrial.ca', 'http://www.bohofurnituregallery.com', 'http://www.dannysfamily.com/', 'http://www.sammysstudentexchange.com', 'http://bellagio.com/nightlife-diversions/hyde.aspx', 'http://thetoytank.com', 'http://www.ironcityarmory.com', 'http://journeyyogawellness.com', 'http://www.gatewayanimalohio.com/?utm_source=yelp&utm_medium=cpc&utm_campaign=jan16', 'http://www.rocksolidconcrete.com', None, 'http://www.ajimenu.ca', 'http://www.precisionpoolcarellc.com', None, '1592234912', 'https://app.visionnv.com', 'https://www.calgarycoop.com/stores/shawnessy/', None, 'http://www.amcofh.org', 'http://www.ironoakshoa.com', 'http://www.z-teca.com', 'http://kendalaquatics.com', 'http://www.hunnerspizza.com', 'http://www.thedistrictatgvr.com/', 'http://www.apple.com/retail/glendale/', 'http://www.marquisdiagnosticimaging.com', None, 'http://www.thewirelesscenter.com', 'https://www.extraspace.com/storage/facilities/us/arizona/phoenix/501788/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'https://athleta.gap.com/stores/wi/madison/athleta-7080.html', 'https://www.usps.com/', 'http://katespade.com', None, 'http://www.nicksauto-tech.aaro.ca', 'http://www.hairmonet.com', 'http://www.greenwaymoving.ca', None, None, 'http://www.winemandental.com', None, 'http://www.mfmassage.com', None, 'https://bluepearlvet.com/hospital/avondale-az/', 'http://www.antheaspa.com', 'http://www.thechateauaz.com', 'http://www.coronetpizzeria.com', None, 'http://www.sabuddyrestaurant.com', 'http://www.avis.com', 'http://www.hendrickmotorsports.com', None, 'http://www.legacyjewelersofpittsburgh.com', 'https://www.dabuzispizza.com', None, 'http://alysskincare.com', 'http://vikingfishandchips.net', 'https://www.applebees.com/en/restaurants-champaign-il/2121-n-prospect-93091', 'http://www.thenailtique.com', 'http://www.shopsys.ca/', '1592235014', None, 'https://www.extraholidays.com/las-vegas-nevada/worldmark-las-vegas-boulevard?lid=yelp&utm_medium=referral-affiliate&utm_source=yelp.com&Identifier=yelp&hotelid=77219&utm_campaign=localpage-worldmarklasvegasboulevard&promoid=localpage-worldmarklasvegasboulevard', None, None, 'http://www.stmlv.org', None, 'http://www.purrclothing.ca', 'http://call4handymanlv.com', 'http://305kustomzdesigns.com', None, 'http://www.theoriginaldicksspeedotach.com/', 'http://visitpittsburgh.com', 'https://batlgrounds.com/axe-throwing-yorkdale', 'http://www.MyLasVegasChiropractor.com', 'http://www.planetdailies.com', 'http://liquorlibrarylv.com', None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, None, 'http://tofoodfest.com/', 'http://snipssalonclt.com/', '1592235069', 'https://www.spencersonline.com/store/Ross-Park/32682040.uts', 'http://thestudioacademyofbeauty.com/locations/chandler-campus/', 'http://www.tinytots.ca', 'http://www.supremecollisioncentre.ca', 'http://www.mobilia.ca', 'http://www.westernexterminator.com/chandler', 'http://www.yorkmillspa.com', 'http://www.stampsautoqueencreekqueencreekaz.com', None, 'http://www.vitalitymwi.com', None, 'https://www.thespacelv.com', 'http://www.rosenbaumrealtygroup.com/', 'http://coolpools.services', None, 'https://www.wellsfargo.com/locator/bank/?slindex=1&il=EN', 'http://longwongsofnorthphx.com', 'http://www.winedowntc.com', 'http://www.mitcoremodeling.com', None, 'http://www.holdenarb.org/home/', 'http://kmedspa.com', None, 'http://www.quickerrooterplumbing.ca/', 'http://pittsburghrugcompany.com', 'https://suncountry.com', 'http://www.fujimiddleton.com', 'http://www.thebeergrowler.net/charlotte', None, 'https://sandpipers.ca', None, 'http://www.starbucks.com', 'http://www.picazzos.com', 'https://www.easystreetgalleria.com', None, None, '1592235155', 'http://www.goodlifefitness.com/locations/ontario/mississauga/toronto-pearson?source=yelp-websitelink-torontopearson-gl', 'https://www.pteglv.com/locations/pts-gold/st-rose-eastern/', None, 'http://www.weldrickanimalhospital.com/', 'https://www.cosmopolitanlasvegas.com/resort/spa?utm_source=yelp&utm_medium=organic&utm_campaign=yelp', 'http://www.idotactical.com', 'http://www.progressive.com/locations/mayfield-heights-campus3/', 'https://elitevacuumsplus.com', 'http://www.vha.ca/', 'http://mwtravelvegas.com/', 'http://www.ezpawn.com/locations/nv/las-vegas/6032-cheyenne', 'https://www.eggsupgrill.com/locations/charlotte-nc/', 'http://www.popculture-comics.com', None, 'http://www.wimpysdiner.ca', 'http://www.shearshades.com', 'https://www.oroexpresschandler.com', 'http://www.forcesofnature.ca/', 'http://tommysdrivein.com', 'http://www.saintbernadette.com', None, 'http://steelcreationsfab.com', 'http://www.VerveStudio.net', 'http://www.performancemufflershop.com', 'https://po-ke.ca', None, 'https://www.usps.com/', 'http://grandcourtmesa.com', 'https://azfoodcrafters.com', 'http://www.ohiocitycycles.org', 'https://www.biltmorecounseling.com', 'http://www.budgetmoversaz.com', 'http://bluewavepoolsaz.com', 'https://www.haggar.com/stores/las-vegas-nv/?utm_campaign=websitelink&utm_medium=Referral&utm_source=yelp', None, 'https://www.coultertempe.com', 'http://www.swimzone.info', 'http://walmart-eyedocs-lasvegas.com/Eastern-Russell', None, 'https://www.calgarypromovers.com', 'http://www.gyrotime.com', 'http://www.dinaalonzibridal.com', 'http://www.massagelifewellness.com', None, 'http://www.shellhospitality.com', None, 'http://www.lakemetroparks.com/parks-trails/farmpark', 'http://www.charlottegeneraldentist.com/', 'http://tomyumthaiaz.com', '1592235283', '1592235286', 'https://www.30sixnoda.com', None, 'https://www.laserquest.com/on-whitby', 'https://yogatothepeople.com/tempe-az/', None, 'http://hairbygk.com/', 'http://www.crookedcue.ca/', None, 'http://www.mission4th.ca', 'http://www.lisatrainer.net', 'http://www.greektownrestaurant.com', None, 'http://arizonasports.com', 'http://www.itmp.com', None, 'http://www.scarboroughnissan.com', None, 'https://www.walgreens.com/locator/walgreens-401+w+main+st-waunakee-wi-53597/id=5669', 'http://www.andrewsco.com', 'https://www.sheridancollege.ca', 'http://www.bloombrossupply.com/', 'https://www.esso.ca/en/gas-station/richmondhill-on-beavercreekesso-200302403', 'http://www.eatatgreenmix.com', 'http://www.seasonsboulangerie.com', 'https://tanwithkare.com', '1592235353', None, 'http://bestnails.webs.com/', 'http://Brilliantnailsspa.com', None, 'http://www.lowes.com', '1592235367', 'http://www.lasvegascaralarms.com', 'http://scottsdaleshadowsarizona.com', None, 'http://www.jjcontractingnv.com', 'http://www.dualimagesmiles.com', 'https://agents.allstate.com/j-c-alvarado-charlotte-nc1.html', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://mnandipies.com', None, 'http://www.ArnoldSmithLaw.com', 'http://www.customcobblersofmadison.com', 'https://stores.anntaylor.com/nv/las-vegas/1013-south-rampart-blvd.html', 'http://www.suncityupholstery.com/', None, 'http://www.dropshade.com', 'http://popeyes.com/', 'http://gyro-spot.com', 'http://www.aircanada.ca', 'http://3apools.com/', 'http://www.associatedasset.com', '1592235418', 'http://www.terribleherbst.com/', 'http://www.studio262salon.com', None, 'https://ad.doubleclick.net/ddm/clk/434191077;236814625;i', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', None, 'http://www.mattressfirm.com', 'http://www.monkeypantsbar.com/', '1592235439', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://westvalleydentalaz.com/', 'https://abraauto.com/abra-auto-location/1051-charlotte-nc-albemarle-road', 'http://www.mrantenna.com', 'http://www.hlwp.co', None, 'http://www.sweetlifebakeshoppe.com/', 'http://www.brueggers.com/', 'http://footsolutions.com/strongsville', None, 'https://locations.dennys.ca/AB/CALGARY/248179', 'http://www.whitneymurphyfuneralhome.com', 'https://essencevegas.com/locations/henderson/', None, 'https://accutempaz.com', 'http://www.chefbar.ca/', 'http://www.mtlebanon.org/index.asp?NID=25', 'http://www.faregamecc.com', 'https://www.umcsn.com/Quick-Cares/Quick-Care-Locations-Summerlin.aspx?intMenuID=112&intPageID=197', 'http://www.safeworksillinois.com', 'https://www.hendrickhonda.com?utm_source=weblistings&utm_medium=organic&utm_campaign=hendricklocallistings', 'http://www.access1alarm.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://vegasnailspa.com', 'http://sarahdiaz.com', None, 'http://www.theblackbullpub.ca', 'http://www.upmc.com/locations/community/family-health-centers/Pages/lawrenceville.aspx', None, None, None, None, None, None, None, 'http://www.vaughnautoglass.com', 'http://www.experttechauto.com', 'http://am.pizza', 'http://dennys.com', 'https://www.smithsfoodanddrug.com/storeHours?store=70600371', 'http://www.themodclub.com/', None, 'https://www.enterprise.com/en/car-rental/locations/us/nv/las-vegas-n-rancho-dr-5427.html?mcid=iyp:8368400', 'http://www.valleyfirefightermovers.com', 'https://www.choicehotels.com/north-carolina/charlotte/sleep-inn-hotels/nc005/rates', None, None, 'http://vcacanada.com/royaloak', 'http://dbarkadz-filipino-cuisine.business.site', 'https://www.chilis.com', None, 'http://nakedbeautybar.com/', None, 'http://www.lakesidespa.ca', 'http://www.trinitybellwoodsflea.com/', 'http://www.drcarolford.com', '1592235578', 'http://sinfulskinaz.com/', 'http://www.elxrjuicelab.com', 'http://www.laide.ca', 'https://totalstoragesolutions.com/storage-locations/arizona/peoria-storage-units/7590-w-olive-ave', None, None, 'http://www.ebgames.com', 'http://www.atomicdogboutique.com', None, 'http://www.championappliancecare.com', 'http://www.starbucks.com/store/351/ca/sunridge-mall2/2525-36th-st-n-e-160-calgary-ab-t1y-5t4', 'http://www.grafgrowers.com', 'http://www.gameworks.com/', 'http://www.septic-systems-calgary.ca/', 'https://www.americanfreight.com/?utm_medium=Yelp_Website_URL&utm_source=Yelp', None, 'http://hmartca.com/hmart/?page_id=17', 'https://ad.doubleclick.net/ddm/clk/458685305;262921492;q', 'http://pastorcameron.com', 'http://www.leslievilledentistry.com/', None, 'http://joemommasgrille.com', 'https://www.cathaybank.com', 'https://www.verizon.com/home/storelocator/pa/pittsburgh-15206/', 'http://www.cartridgeworld.com', 'http://www.electricdaves.com', 'http://www.mistwoodapartments.com', 'http://daveandbusters.com/?utm_source=DB&utm_medium=Text&utm_term=DB&utm_content=WebsiteLink&utm_campaign=DB_DB_Text_WebsiteLink', 'http://www.callitspring.com', 'http://wreckamendedautobody.com', 'http://www.thisiscleveland.com', 'http://www.chevron.com', 'http://www.marijuanadeliveryline.com/shop', 'https://www.plantarestaurants.com/location/planta-queen/', 'http://www.kumon.com/SUMMERLIN', None, 'https://locations.wendys.com/canada/qc/lasalle/8699-boul.-newman', 'http://www.kabobnmore.com', None, None, 'http://www.kfc.ca/store/sunrige-mall-101-2525-36-st-ne-calgary', 'http://perpetualfitnesscle.com', 'http://sfdslv.org', None, 'https://whitesintegrityauto.com', None, 'http://www.tommiegirlphotography.com', 'https://www.sprint.com/storefronts/bd/sprint-phoenix-az-85022-fcs-1908/?ecid=SEO:Yelp:2020_Q1:LastMile', 'https://www.ceenta.com/locations/huntersville', 'http://flyingmonkeytruck.com', None, 'http://www.allysphotography.ca', 'http://www.nailganic.me', '1592235698', 'https://bailbondsusa.com', None, 'https://fullypromoted.com/locations/scottsdale-az/', '1592235706', None, 'https://www.localfirstaz.com/events/fall-festival', None, None, None, 'https://sugardaddyscafe.com', 'http://vitalitymds.com', 'http://www.muramoto.biz', 'http://www.7forallmankind.com', 'http://www.susysoup.com', 'http://treesbymikearizona.com', '1592235733', 'http://www.pilatesofcharlottenc.com', '1592235738', 'https://www.hungryhowies.com/store/hungry-howies-00876?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=00876&utm_content=Website_Link', 'http://www.riddleroom.ca/', 'http://www.torchedgoodness.com/', 'http://www.precisionspecialtypharmacy.com', 'https://www.lhmnissanmesa.com', 'http://bit.ly/RealtyExecsTempeTower', 'https://smallpeoplepreschool.com', None, 'https://www.bobevans.com/our-restaurants/locations/571?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.wetzels.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=8658&localechange=1', None, 'http://Bundtsnbutter.com', 'http://www.arizonajewelryappraisals.com', 'http://paisleymonkey.com', 'https://www.euroworks.ca', 'http://www.maltzmuseum.org/', 'http://www.akronphotographer.com', None, 'http://www.firegrill.com/', 'http://www.hairoriginalsalonstudio.com', 'http://azdollhouse.com/', 'http://www.gracelutheranhenderson.org', 'http://thepopplacestore.com', None, 'http://www.widmaierchiropractic.com', None, None, 'http://www.toronto.ca/parks/prd/facilities/complex/287/index.htm', 'http://tokyodiscountvegas.com', None, None, None, None, 'https://www.redrobin.com', 'http://www.pranjbeauty.com', None, None, 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://www.structube.com', 'http://popeyes.com', 'http://in.puma.com', 'https://www.discounttire.com/store/az/gilbert/s/1418?utm_source=yelp&utm_medium=social&utm_campaign=YelpBusLinkClick', '1592235832', 'http://totum.ca', None, None, 'http://www.bestofthebestdjs.com', None, 'http://www.gungarage.com', 'http://www.sunsetvillaaz.com', 'http://cornerstonegiftsandpo.com', None, None, None, 'http://calibercollision.com/locate-a-caliber-collision-center/surprise', 'http://www.desertstorage.com/scottsdale-az-storage-units', 'http://www.scottsdalecc.edu', 'http://www.cupkateslv.com', 'http://www.caesarspalace.com/restaurants/empress-court.html#.Ugfc5su9KSM', 'http://www.brossardbagel.com', 'http://www.mrchickencle.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://locations.avis.com/us/az/chandler/ca3.html', 'http://www.modoyogalasvegas.com', '1592235882', '1592235884', 'https://www.valleyhealthphysicians.com/find-a-doctor/hazem-afifi', 'http://Surprisecomics.com', 'http://www.smileycrane.com', None, 'http://allstateappliancelv.com/', 'http://johnnyrockets.com/', None, 'https://www.mesaparks.com/parks-facilities/parks/countryside-park', 'http://www.monarkhome.com/showrooms/las-vegas', 'http://www.steinmart.com', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/109+Dabney+Drive-Henderson-NC-27536/storeid=7055?cid=ps_ylp_2020', 'http://www.dillonazrealty.com', 'http://www.arizonaplumbingservices.com', '1592235919', 'http://www.lasvegaspilatesyoga.com', 'http://www.deeppilates.com', 'http://www.irepairicustomize.com', None, 'https://www.hilton.com/en/hotels/clttght-home2-suites-charlotte-i-77-south-nc/?SEO_id=YELP-HT-CLTTGHT', 'http://www.capitalacctpc.com/', None, 'http://www.jamminjumperoos.com/', '1592235936', 'http://www.frozen75.com', 'http://Tamerabbit.com', 'https://bounceu.com/gilbert-az', 'http://www.bullseyesvc.com', None, 'http://popeyes.com', 'http://www.fastfreshfoods.ca/', None, 'http://www.palmsouthwest.com', 'http://www.jeguitars.com', 'http://www.carrefourrichelieu.com/fr', None, 'http://Www.2womenandasolution.com', 'https://www.simonmed.com/locations/all/simonmed_imaging___maryland', 'http://www.RobinsonAutoDetails.com', 'https://stores.fossil.com/az/gilbert/santan-village-8252/', None, '1592235970', 'http://www.cleveland.hfitcenter.com/', 'http://www.bk.com', 'http://phoenixcoffee.com', None, None, None, 'https://www.lovencarevet.com', 'http://www.saintjohncathedral.com', 'https://www.ryokujudo.com', None, 'http://www.tacotimecanada.com/locations/ontario/ajax/ajax', '1592235997', None, 'http://qdoba.com', None, 'http://roomsonline.ca', 'http://www.prada.com/', 'http://www.cigna.com/cmgaz/locations/san-tan-medical-office', 'http://www.innergroovebrewing.com', 'http://www.drtorgerson.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://freshandclear.com', 'http://www.starbucks.com/store/9298/', None, 'http://www.kingbalancing.com', None, None, 'http://www.atlwings.com', 'http://www.cuttyfresh.com', 'https://cleancutlandscaping.us', 'http://www.luxuryhomesofhenderson.com', None, 'http://www.sagebrushranch.com/', 'http://snapfitness.com/waxhawnc', 'http://www.bergo.ca', 'http://www.smilesavvydentistry.com/', 'https://www.purebarre.com/location/dana-park-az', 'https://www.hooters.to/toronto-airport', 'http://www.zenq.ca', 'http://www.drshaunachristensen.com', None, None, 'http://www.kingflyspirits.com', 'http://www.theradiodoctor.com', 'https://www.tirediscountdepotinc.com/cleveland', 'https://www.bobevans.com/our-restaurants/locations/357?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.strattonrestoration.com', 'http://www.Liorthebaker.com', 'http://rmtmassagetherapytoronto.com', None, 'http://fiscalfitnessphx.com/', 'http://banderarestaurants.com/locations/scottsdale/', 'https://www.state48brewery.com', None, '1592236095', 'http://www.quiktrip.com', 'http://www.almikestavern.com', 'http://www.earnhardttoyota.com', 'http://www.clairhursteyecare.com', 'http://mybodyworkz.com', 'http://www.envoquemd.com/', 'http://rvcomplete.com', None, 'https://www.steinmart.com/?utm_source=yelp.com&utm_medium=social&utm_campaign=yelp_site_store48', 'http://www.familyfocusedeyecare.com', 'https://www.obonsushi.com/scottsdale-quarter', None, None, 'https://www.choicehotels.com/arizona/youngtown/quality-inn-hotels/az453/rates', 'http://pizzeriaenzo.com', 'http://www.fitzgeraldsbnb.com', 'http://www.steeltownpaintball.com', '1592236142', 'http://www.timelesstattoolv.com', 'https://www.starbucks.ca', None, 'http://www.landmarkworldwide.com/customerservice?utm_source=yelp_sea&utm_campaign=support&utm_medium=website&utm_content=https', 'http://www.southtowndentalcare.com/', 'https://shinynailsonhappyvalleyglendale.com', 'http://www.foothillsrehab.com/', 'http://www.kay.com', None, 'http://www.azcustomhats.com', None, 'http://www.gokartsatpolsonpier.com', 'https://www.jamesacarytreeservice.com', 'https://artscommons.ca/rentals/venues/max-bell-theatre/', 'http://www.medoneaz.com/', 'http://www.destinocalgary.com/', None, 'http://www.futureshop.ca/', 'http://www.thingsremembered.com', 'http://www.restoamir.com/', 'http://www.kay.com', 'http://www.sunguntanning.com', None, 'https://www.scottsdalemusicaltheater.com', 'http://www.terrysauto.extremewrench.com', None, 'http://www.tupelohoneyteas.com', 'http://www.cliftonmartini.com/', 'http://www.oddballpets.com', None, 'http://www.lcbo.com', 'http://www.azrollerderby.com', 'https://www.chilis.com', 'http://www.brooksbrothers.com/?CMP=SMC_Yelp_6038', None, 'http://thecornerspot.ca', 'https://www.wyndhamhotels.com/hotel/03733?tel=18005369326&iata=00093785&cid=fe:se:20161215:yl:pp:seus:03733', 'https://stores.bareminerals.com/az/chandler/us-3/', 'http://deluxenailsbar.com', 'http://www.watsonsglen.com', None, 'http://www.2andhighbar.com', 'http://www.alpineroofing.ca', 'http://www.klingshirnwine.com', 'https://www.theranchestates.com', None, None, None, 'http://www.crowntownathletics.com', None, None, None, 'https://www.westgateresorts.com/hotels/nevada/las-vegas/westgate-las-vegas-resort-casino/', 'http://www.marshallsonline.com/store-finder/204', 'https://www.bellamirageapts.com', 'http://www.dvpeds.com', None, 'http://sololiquor.com', None, 'http://www.shampoochgrooming.ca', 'https://keepitcut.com', None, 'http://www.benjerry.com/', None, 'http://www.weissmeats.com', 'http://www.thegreenhouseflorist.com', None, 'http://www.halecoffee.com', 'http://www.mycompletepoolcare.net', 'http://www.ranchodetiarosa.com/rancho-chandler.asp?expanddiv=all', 'http://www.mokshayogaaurora.com', 'http://mrlube.com', None, 'http://www.textbookpainting.com', 'http://www.hansenortho.com', 'https://www.highlandparknorthlake.com', 'https://www.ulta.com/stores/madison-ms-477', 'http://www.saltrivereyecare.com', None, 'http://www.knuckledownsaloon.com/', None, 'http://www.westsidemarket.org/vendor.aspx?id=69', None, None, 'http://deseretindustries.org', 'http://www.marcs.com/stores/marcs-north-ridgeville-grocery-store-44039.aspx', None, None, 'http://www.phoenix.edu', None, None, 'https://www.marcos.com/locations/nc/gastonia/w-garrison-blvd', 'http://www.steelcityflooring.com/', 'https://vrjunkies.com/vr-junkies-az/', 'http://sears.com/stores/massachusetts/cambridge/0001343.html', 'http://www.legionbrewing.com', None, None, 'http://www.dukesbread.com', None, 'http://www.jellybeenz.com', 'http://www.urbanbean.ca', None, 'http://www.labellavitacleveland.com', 'http://www.sash.ca', 'https://www.choicehotels.com/CN659?mc=blypypaf', 'http://www.aceparking.com/downtown-phoenix-parking.com', 'http://www.careytechsolutions.com', None, 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', None, None, 'http://armorpestdefense.com', 'http://www.heidisbrooklyndeli.com', 'http://ilanmassagestudio.com', 'http://bdcustomtattoos.com', 'http://www.ntb.com/store/6234/mayfield-heights-oh-44124-2905?utm_source=yelp&utm_medium=maps&utm_campaign=yelp-maps', None, None, '1592236410', None, '1592236415', None, 'http://www.hightails.ca', 'https://www.agelesskarate.com', 'http://www.mpautobodyrepair.ca', 'http://www.carlstreeservice.net', 'http://www.tailoredeventslv.com', None, '1592236432', 'http://www.solairespa.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.exosathome.com', 'http://dentalbobw.wix.com/denturerepairs', 'https://www.sleepez.com/?utm_campaign=Yelp&utm_source=yelp&utm_medium=referral', 'http://hamiltonortho.com', 'http://www.rbinc-sports.com', 'https://www.pikebeverage.com', 'http://ccandcompanysalonspa.com/', None, 'https://www.cleanjuice.com/locations/uptown/', 'http://srwc.unlv.edu/', 'http://www.theronceyhotel.com/home.html', None, None, 'http://www.702-pools.com', None, 'http://www.belmontapts.com', 'https://www.thehealingquest.com', 'http://robertostacoshop.com', 'http://www.charlottegolf.com', 'https://www.haircutmencorneliusnc.com', None, 'http://www.tymaz.com/', None, None, None, 'http://www.coquettepatisserie.com', None, None, 'http://www.alisfashion.com', None, 'http://www.yogurtys.com', 'https://torontoanimaleyeclinic.com', None, 'http://www.teamrossman.com', 'http://www.firehousemovingco.com', None, 'http://constanthomecomfort.com', None, 'http://www.wcequestrian.com', 'http://warehousewars.net', None, None, 'http://www.baselineflowers.com/', 'http://luccaclothing.com/', 'http://www.ilovekickboxing.com/kickboxing-studio/index.php?id=374?utm_source=review&utm_medium=yelp&utm_campaign=referral%C3%8A', 'http://www.azdmovers.com', None, None, 'http://www.harveycatshotel.com/', 'http://www.bk.com', 'https://www.allinclusiveconcretesystems.com', 'http://www.raintreerestaurantchagrinfalls.com/', 'http://nisstech.com', None, 'http://www.ciaociaopizza.com/', 'https://www.bestcharlottemassage.com', 'http://www.LisaYoungDDS.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=1962&localechange=1', 'https://fullpoolservices.com', 'http://www.theparlorlv.com', None, 'http://tonysautoworks.net', None, 'http://nolinesbydesign.com', 'http://local.buckle.com/AZ/GLENDALE/331/?utm_source=Buckle&utm_medium=Website&utm_campaign=Store+Locator', None, '1592236581', None, None, 'http://wyattorthodontics.com', 'http://www.staxburgerbistro.com', None, 'http://www.progressivepavers.com', 'https://www.storagewest.com/facilities/baseline/?utm_source=YelpCTA&utm_medium=referral&utm_campaign=baseline-business', 'http://www.crowdpleezersbarbershop.blogspot.in/', 'http://www.AltierDental.com', 'https://www.victoriassecret.com/store-locator#/store/442', 'http://www.wickedclub.com', None, '1592236611', 'http://www.containerstore.com/locations/showStores.htm?zipCode=28211&searchArea=100', None, None, 'https://lljcustoms.com', None, 'http://www.kohakitchen.com', 'https://locations.wendys.com/united-states/pa/bridgeville/1125-washington-pike', 'http://toba.ca/', None, None, None, 'http://www.renue.ca', 'http://www.mobilehomedepot.net', 'https://www.rubytuesday.com/', 'http://www.odiagasautosales.com', None, None, 'http://www.rivieraopticare.com/', 'http://www.showcasemotorspa.com/', None, 'http://www.azsleepyteepee.com', 'http://giantjones.com', None, 'http://www.marcos.com/locations/oh/berea/w-bagley-rd?s=true', 'http://www.pimadental.com', None, None, None, 'https://www.centerforsightlv.com', None, None, 'http://stores.bestbuy.com/122/', None, 'http://www.averyonthegreen.com', 'http://www.krispykrunchy.com/locations/wy-market', None, 'http://www.thecamptc.com/location-gilbert', 'http://www.saigonpearl.ca', 'http://www.posaresalons.com', 'http://www.sanrio.com', 'http://Islandstylepools.net', 'https://turningpointbeauty.com', None, 'http://www.reneesmassotherapy.com', 'http://johnnyrockets.com', None, 'http://funkytoque.com/wellington-accueil/', 'https://www.smithsfoodanddrug.com/storeHours?store=70600354', None, 'http://therabbitspot.com/the-rabbit-hole/', 'http://www.psdm-madison.com', 'http://www.tizzerts.com/', 'http://flahertytree.com', 'http://www.saddlebroncgrill.com', 'http://www.dwmeats.com/', 'http://www.malleys.com', 'https://www.sprint.com/storefronts/bd/sprint-goodyear-az-85338-d-8157/', 'http://expertcarcareandtransmissions.com', 'http://www.themakeden.com/', None, 'http://www.arbys.com', None, None, None, 'http://www.cupcakejunkiecafe.ca/', None, 'http://www.carolinascornerstone.org', None, 'http://joinswift.com/landing-pages/DR/student/yp/careerhorizon/lp', 'http://monogramcoffee.com', 'http://www.littlecaesars.com', None, 'https://www.fastmed.com/urgent-care-centers/scottsdale-az-walk-in-clinic-mcdowell-road/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', 'http://www.stagsfamilychiropractic.com', None, 'http://www.luxhairsalon.com', 'http://www.fiveguys.com', 'http://www.smittys.ca', 'https://locations.dennys.com/MO/INDEPENDENCE/248531', '1592236785', 'http://www.wellnessmedspacosmetics.com/', 'http://sungshouse.com', None, 'http://www.gaatithaikitchen.com', 'http://www.starbucks.com/', 'http://www.augustoalgusto.com/fr/', None, 'http://www.thegroceryohc.com', 'https://www.mcalistersdeli.com/locations/il/peoria/4810-north-university-street-1289?utm_campaign=yelp&utm_medium=referral&utm_source=yelp&utm_content=1289', 'http://www.kangsbba.com', 'https://www.4patientcare.ws/wsv3pro/web/webschedulerv3.aspx?SessionID=2050207', 'http://noahsarkpediatrics.com/', 'http://eosfitness.com/location/north-scottsdale?utm_campaign=north-scottsdale&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', 'https://www.jandbhauling.com', 'http://goodboydogs.ca', None, 'https://www.tajo-one.com', 'https://www.barkbusters.com/dog-training-charlotte-south', 'http://studiobell.ca', None, 'https://stores.jcrew.com/en/crocker-park?srccode=X%7CPMG%7CNaturalSearch%7CLocal%7CYelp%7C677', None, 'http://www.allseasonsmaintenanceandlandscaping.net/', 'http://www.reborncabinets.com', 'http://mikadosushirobata.dining.ca', 'http://www.orchidspa.net/', None, 'https://www.rolandswigsalonmatthews.com', 'http://www.vegashottubs.com', 'http://hammertoronto.com', None, 'http://www.badassjacks.ca', 'https://www.hilton.com/en/hotels/phxmdgi-hilton-garden-inn-phoenix-midtown/?SEO_id=YELP-GI-PHXMDGI', 'https://www.180smoke.ca/vape-shop-etobicoke-islington-electronic-cigarettes', None, 'http://www.burtonstudio.vegas', 'http://mississaugabarbershop.com', None, None, 'http://www.terribleherbst.com/', None, 'http://www.alovingleash.com/', None, 'http://emeraldcomputers.com/', None, 'http://www.cookout.com', 'http://www.acupuncturecenteraz.com/', 'http://www.TheKyotoBowl.com', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216347&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https:%2F%2Fwww.pizzahut.com', 'http://skintologyrx.com', 'http://leafandplate.tumblr.com', 'http://www.ballyslasvegas.com/restaurants/sea-the-thai-experience.html#.UkB2BsZnGoM', 'http://www.beinlovedesigns.com', 'https://www.athome.com/store-detail/?StoreID=Pennsylvania-Pittsburgh&utm_source=yelp&utm_medium=paidprofile', 'https://locations.theupsstore.com/pa/white-oak/1985-lincoln-way?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://eclipseautobody.com/', None, None, 'http://www.saltchaletarizona.com', '1592236923', 'http://www.rlemb.com', None, 'http://earlymercy.com', 'http://www.lpmproduction.com', 'http://www.nobullburgers.ca', None, None, 'http://www.wilsonstaekwondo.com', 'https://www.autozone.com/locations/az/avondale/10815-w-indian-school-rd.html', 'http://www.chilis.ca', 'http://eighteeneight.com/north-scottsdale-az/?utm_source=yelp&utm_medium=organic&utm_content=weburl', None, 'http://www.zenlia.com', None, None, 'http://www.bowwowdoggiedaycare.com', 'http://www.teakwoodstavern.com/', 'https://rolliciouscreamery.com/madison-1', 'http://www.goldcoastcasino.com', 'http://www.beinsoccer.com', None, None, 'http://www.vegasthedj.com', 'https://local.fedex.com/oh/mayfield-heights/office-1225/', 'https://stores.golfgalaxy.com/nc/charlotte/3039/', 'https://www.positivelyfrosted.com', None, 'http://www.azactorsacademy.com', None, None, 'http://www.rockymountainsoap.com/', 'https://pracharlotte.com/location/charlotte-cotswold-eastover/', 'https://www.taravietnamesegrill.com', None, 'http://www.ubreakifix.com/locations/pittsburgh', None, 'http://www.splaw.net/', 'https://www.olivegarden.com/locations/az/mesa/southern-fiesta-mall-west-mesa-alma-school-rd/1661?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:mesa-az-1661_pl:locurl_rd:1517', 'http://www.portofsubs.com/', None, None, 'http://www.concentra.com', 'https://www.deshonpullenlaw.com', 'http://www.mcfarlandlibrary.org/', 'https://www.wellsfargo.com', 'http://www.LegalRide.com', '1592237028', 'https://www.trainerpaul.com', None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', '1592237043', 'http://www.cefiore.com', 'http://www.roncesvallesanimalhospital.com/', 'http://jokercafe.info/', 'http://www.traderjoes.com', 'http://www.alohayogurt.com', 'http://www.outdoorlivinglv.com', 'http://www.litespressobar.com', None, 'http://www.mikesgranite.com', None, None, 'https://www.spectrumoralandfacialsurgery.com', None, 'http://www.mpi-services.com/', None, 'http://www.senseandcolor.com/weddings', 'http://gexwomenscare.com/', 'http://www.alleghenyvet.com', 'http://www.reclaimedsecrets.com', 'http://www.desertskyfamilydental.com', 'http://www.greenleafarrowheadranch.com', 'http://www.discount-drugmart.com', 'http://www.trueshinerimrepair.com', 'http://www.brars.ca', 'http://www.eagleindustriescorp.com', 'http://www.discountcab.com/', 'http://muddypawslv.com', 'http://cherryontop.net/', None, 'https://www.zoup.com', 'http://www.beckseuropean.com', 'http://www.ejsushi.com', 'https://locations.monro.com/pa/crafton/2175-noblestown-rd?utm_source=yelp&utm_medium=referral&utm_campaign=yelp', 'https://egl-junk-removal-lasvegas.business.site', 'http://pandora.net', None, None, 'http://www.drpease.com', 'http://www.zimbrickbuickeast.com', 'https://www.gessweinsclocks.com', 'https://www.huntington.com/Community/branch-info?locationId=625', 'http://www.tremontmusichall.com/', None, 'https://killumpestcontrol.com', None, 'http://fitnessconnection.com/clubs/southpark/', None, 'http://smiledocsaz.com', 'http://www.pinkislaserspa.com', 'http://www.empowerpt.com', '1592237155', None, 'http://www.artofshoerepair.com', 'http://www.starbucks.com/store/1013599/', 'https://www.londondrugs.com/london-drugs-store-030-calgary/heritage-plaza-030.html', 'http://www.libertymutual.com/brian-weaver', 'http://www.beansproutscafe.com', 'http://www.capitalone.com', 'http://www.kidzrockprep.org', 'http://www.lvsurgical.com', 'http://goharvestmarket.com', '1592237180', 'http://www.scottsdaleautosalon.com/home', 'http://www.studioadt.com/', 'http://www.bamdogwash.ca', 'http://www.staytruebodyart.com', 'http://www.liveatthepavilions.com', 'http://www.restaurantkarma.com', None, 'http://ifadevegas.com', 'http://www.loirerestaurant.ca/', 'http://www.flrpropertymgmtphoenix.com/', 'http://www.mrchickencle.com', None, 'http://cibronebakery.com/index.html', 'https://locations.timhortons.com/ca/on/richmond-hill/1070-major-mackenzie-dr.html', None, None, 'http://www.newlookhairnailandspa.com', 'https://www.elitemusic.ca', None, None, 'http://pageskensington.com/', 'https://www.bobevans.com/our-restaurants/locations/266?utm_source=yelp&utm_medium=listing&utm_campaign=fall_fy20', 'http://www.deseretfamilymedicine.com', 'http://algobertoslasvegas.onlunchroom.space', None, 'http://www.prettyyongething.com', 'http://www.solarpenny.com', 'http://www.southernnevadalocksmith.com/', 'http://www.wongsphoenix.com', 'http://www.dsw.com', 'https://palmbeachtan.com/locations/AZ/Peoria-West-Thunderbird-Road/?utm_source=Yelp&utm_medium=banner&utm_content=website&content=PHX', 'https://mountainsidefitness.com/locations/gilbert/', None, 'https://ad.doubleclick.net/ddm/clk/434177199;236814625;r', 'http://stlouiswings.com', None, 'http://www.posaresalons.com/', 'http://actionappliances.net', 'http://www.riteawayservices.co', None, None, None, 'http://www.buymaytag.ca', None, 'http://www.zibabeauty.com/', 'http://www.eternalhealthandwellness.ca', 'http://hoangthynailsspa.com/', 'http://www.kimmyztatumpoint.com', 'http://www.fisherkingwinery.com', 'https://lasvegas.colormemine.com', None, 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://www.surlatable.com/browse/storeCalendar.jsp?storeId=137', None, 'http://www.spalv.com', 'http://www.fhtaz.org', 'http://www.shell.com', 'http://hgsystemintegrators.com', 'http://littlawfirm.com/', None, 'https://duckdonuts.com/locations/huntersville-nc-rosedale-shopping-center/', None, 'http://pittsburghpetgrooming.com', 'http://www.drkintonis.com', 'http://www.daniadown.com', None, 'http://www.azrealtycare.com/', 'http://www.basspro.com/webapp/wcs/stores/servlet/CFPageC?storeID=55&storeId=10151&langId=-1&catalogId=10051&tab=3&appID=94', 'http://www.omgbakedgoodness.com', None, None, None, 'https://www.usps.com/', 'http://drupatis.com', '1592237356', 'http://www.launicahuntersville.com/', 'http://www.ardene.com', 'https://www.roots.com/on/demandware.store/Sites-RootsCA-Site/default/Stores-StorePage?storeId=187&cm_mmc=YELP-_-CANADA-_-WEBSITEURL-_-187', 'http://yourazbraces.com', 'http://www.parkwaychiropractic.net', 'https://cutrateglass.com', '1592237372', 'https://www.kohls.com/stores/nv/lasvegas-669.shtml?utm_source=rio&utm_medium=referral&utm_campaign=yelp', 'https://www.centropolis.ca', None, 'http://www.mvnailspa.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, 'http://www.wildwestmercantile.com/cgi-bin/Category.cgi?category=home&type=store', 'http://www.rosetuxedoaz.com', 'http://www.starbucks.com/store/9681/', 'https://www.therange702.com', 'http://www.mccalls.ca', 'http://www.chefkebab.ca', 'http://drjsoffice.com', '1592237404', 'http://www.waterjack.com', 'http://gonyfl.com', 'https://www.walgreens.com/locator/walgreens-275+davison+dr-sun+prairie-wi-53590/id=3291', 'http://www.kwalitysweets.com', 'http://velocitycx.com/', 'http://www.carolinashealthcare.org/cabarrus-pediatrics-map-and-directions', 'http://www.sheawomenscare.com', 'https://www.anytimefitness.com/gyms/2744/University-Heights-OH-44118/?utm_source=yelp&utm_medium=local', None, 'https://signup.myiclubonline.com/iclub/newAgreement/0389/selectPlan.htm', 'http://www.yogurtvi.com', 'http://www.venetian.com/nightlife/bars-and-lounges/the-bourbon-room.html', 'http://tropicaldelightscharlotte.com/', 'http://www.countryinns.com/champaignil', '1592237438', None, 'http://www.thecandybar.ca', None, 'http://www.pdqstores.com/gmaps/Wisconsin/MadisonArea/135.html', None, 'https://pho-fordays.com', None, 'https://www.sonoraquest.com/find-a-location/glendale-59th-ave-eugie/', 'http://www.queencitytours.com', None, None, 'http://www.atriasunlake.com', 'http://www.duetcatering.com', 'https://www.target.com/sl/charlotte-midtown/2244', 'http://www.starbucks.com/store/9298/', 'https://www.chick-fil-a.com/arboretum', 'http://marusakebar.com/', None, 'http://www.salazarusedcars.com', 'http://www.arizonadeck.com', None, 'http://www.jerusalemgrill.com', None, 'https://www.circlek.com/store-locator/us/phoenix/19830-n-7th-st/2706643', 'https://www.drtarapeyman.com', '1592237494', None, 'http://www.redcareers.com/kwrpp/', 'http://www.spiedini.com/', 'http://www.marvelousepoxyflooring.com', 'https://order.littlecaesars.com/en-us/stores/15150003/10720-e-southern-ave/mesa/az/menu', None, 'https://bhmanagement.com/communities/the-venue-on-camelback/', 'http://www.greencardadvice.com', 'http://erabyciara.com/', 'http://www.zocalobistro.com', 'http://tyrell710.wix.com/fingertips2thesoul', 'http://www.marshallsonline.com/', 'http://650cafe.com/', 'http://www.astaraskincare.com', 'http://www.arrowheaddermatology.com', '1592237535', 'http://www.serviceking.com/locations/service-king-penn-hills?utm_source=yelp&utm_medium=local&utm_campaign=yelp-profile', 'http://locations.michaels.com/az/mesa/2778/?utm_campaign=Google+Places&utm_medium=Maps&utm_source=Google', 'http://www.centurylink.com', 'https://locations.jackinthebox.com/us/ca/concord/1710-monument-blvd', None, 'http://www.dads-smokeshop.com', 'http://www.friendlyneighborhoodhelp.com', 'https://www.olivegarden.com/locations/oh/parma/parma-town-mall/1128?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:parma-oh-1128_pl:locurl_rd:1083', 'http://www.beautifulskinbylucy.com', 'http://www.ritasfloraldesigns.com', 'https://ad.doubleclick.net/ddm/trackclk/N3493.Yelp/B24050224.272429163;dc_trk_aid=466899273;dc_trk_cid=127976389;dc_lat=;dc_rdid=;tag_for_child_directed_treatment=;tfua=', None, 'http://www.arcelectriccompany.com', 'http://www.7-eleven.com/?yelp=29384', 'https://locations.massageenvy.com/arizona/scottsdale/8752-east-shea-blvd-ste--c-3b.html', None, None, 'https://redrock.sclv.com/Gaming/Race-and-Sports-Book?utm_source=Yelp&utm_medium=organic&utm_campaign=fb&utm_content=listinglink', 'https://www.target.com/sl/las-vegas-blue-diamond/2164', 'https://www.arashijapansteakhouse.com', 'http://www.mgpaz.com', 'http://www.silversnail.com', None, None, 'http://www.ajsfinefoods.com', 'http://www.lasvegasguitarteacher.com', 'http://www.trilogypoolsaz.com/', 'http://poshpooches.ca', 'http://www.aleromoving.com/', None, 'http://www.litchfieldauto.net', 'https://www.crowncustomtattoo.com', 'http://www.illinismilesdental.com', None, 'http://www.udallattorneys.com', 'http://www.rvmastertechs.com', None, 'http://www.buffaloscafe.com', 'http://www.bengioielli.com', None, 'http://www.moulinbouge.com', 'http://birkdalevillage.net/portfolio/birkdale-village-cleaners', 'http://Munhallvet.com', 'http://www.hillhurstmortgage.com', 'https://www.zaxbys.com/locations/sc/fort-mill/3401-hwy-21/', None, 'https://www.bestwestern.com/en_US/book/hotel-rooms.03157.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03157', 'http://ilfornello.com/richmond-hill/', None, None, None, '1592237668', 'http://www.bigotires.com/regions/minneapolis-metro', None, None, None, 'http://Www.electrikneedletattoo.com', 'http://www.apachetaxi.com', 'http://www.ibdaz.com', 'http://www.gfsbjj.com/', None, 'http://www.matthewsalehouse.com', 'http://www.antoniospizza.net', None, 'http://eastvalleyurban.com/phoenix/stella', 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', None, None, 'http://DDLDental.com', 'http://familydentalstudio.net', None, None, 'http://www.friendsofthewild.org', 'http://www.libertymutual.com', None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.einsteinbros.com/', 'http://www.paradisebaypetresort.com/', 'http://www.everlastingchanges.com', 'http://www.quiktrip.com', 'https://www.lesliespool.com/?utm_source=yelp&utm_medium=social%20media', 'http://thebeatbooth.com', 'http://babycakeswilloughby.vpweb.com', 'http://www.arizonastone.com', 'http://www.newdirectionfertility.com', 'https://www.vegaslashlounge.com', '1592237755', '1592237758', 'http://www.thecurzon.ca', None, 'http://www.samsbarbershops.com', 'http://www.imeldasmith.com', 'http://tinkers-handyman-service.business.site', 'http://www.starbucks.com', None, None, 'http://www.shaggyshaggyshake.com', None, None, None, None, None, 'https://www.supercuts.com/locations/nv/henderson/eastern-commons-haircuts-9195.html', None, None, None, 'http://pho87.net', None, 'http://poolpartsplus.net/', 'https://www.dominionselfstorage.net/self-storage/az/queen-creek/dominion-self-storge-queen-creek/unit-sizes-prices', None, 'http://www.sherwin-williams.com/store-locator/paint-store/Las%20Vegas/NV/8114', 'https://www.greatvaluestorage.com/self-storage/las-vegas-nv-92971', 'https://konjikiramen.com', 'http://yackodentistry.com', 'https://www.podiatryinc.com', 'http://www.freewayinsurance.com', 'https://chocolateshops.sees.com/az/phoenix/chocolate_shops_phoenix_az_102103.html', 'https://acesandarrows.com', 'http://www.noisette.ca/index.html', 'https://locations.cinnaholic.com/ll/CA/ON/Scarborough/6015-Steeles-Ave-E', 'https://www.sunnysidehonda.com', None, None, None, 'http://www.bwsweetsbakery.com', '1592237855', None, 'http://www.charlotte.studio-cellar.com', 'http://www.xooro.com', 'https://www.sonoraquest.com/find-a-location/phoenix-by-appointment-only-tatum-shea/', 'https://www.cellphonerepair.com/charlotte-uptown-nc/', 'https://ad.doubleclick.net/ddm/clk/458685299;262921492;c', 'http://www.somunsuperstar.com', '1592237871', 'http://www.archeryhq.com', 'https://www.agoracleveland.com', 'http://victoryenergywellness.com/', 'http://www.geeksnthings.com', 'https://nodabrewing.com', None, 'http://phoenix.sentrymgt.com', 'http://www.caringheartsanimalclinic.com', 'http://www.stellavapors.com', None, 'http://www.prohibitionclt.com/', 'http://scenicbrewingcompany.com', None, None, None, 'http://justpuckit.com', 'https://www.avioflower.com', 'http://www.bbhairringtons.com', 'https://www.olivegarden.com/locations/oh/north-olmsted/north-olmsted-great-northern-mall/1133?cmpid=br:og_ag:ie_ch:dry_ca:OGQ121LOCURL_dt:20200604_sn:yelp_gt:north-olmsted-oh-1133_pl:locurl_rd:1087', 'http://www.chousky.com', 'https://speedstarautotransport.com', 'http://www.kolornkiln.com', 'https://www.b1locksmith.com/chandler-locksmith', 'http://www.gamestop.com', 'http://www.gamestop.com', 'http://www.littlecaesars.com', 'http://www.fetaolivesgrill.com', 'http://pittsburgh.vettechinstitute.edu', 'http://luna-street-food.business.site', 'http://centurymill.com', 'http://www.BeestungLingerie.com', 'http://www.rapunzelhair.ca', 'http://www.reliableautolv.com', 'http://extremevaluestore.com/', None, 'https://www.happyaxe.com', 'https://kipc.vegas', None, None, None, None, 'http://www.coastappliances.com', 'http://www.phoenix.egoscue.com', 'http://www.bartonsbakeshop.com', 'http://www.banfield.com/veterinarians/wi/madison/emn?utm_content=yelp_general&utm_medium=PAID&utm_source=yelp&utm_campaign=YelpPaid', 'http://www.homehardware.ca/en/dealer-microsites/1274-8/contact-information.htm', 'http://www.europeanmotorstudio.com', 'https://wildfire.sclv.com/The-Greens', 'http://www.boosterjuice.com/', '1592237980', None, 'http://uniquepatiocreations.com', 'http://www.wexlerstavern.com/', 'http://theplacearizona.com', None, 'http://www.mtlebanonfloral.net/?srccode=yelp_track', '1592237997', 'https://thepetclub.com', 'http://www.encompasshealth.com', 'http://www.dimanddensum.com/', 'http://www.wingatehotels.com/hotels/hotel-overview?wid=ps%3Aaddppc_yelp&tel=18885953511&reg=appc-_-YLPROPP-_-30442-_-winwes&hotel_id=30442&cid=whg_winwes_yelp', 'http://dekra.us/en/nevada/las-vegas-3430-e-tropicana-ave/', 'http://lasvegassolarinstallation.com', 'http://www.hairpieceslv.com', 'http://www.thecharlestondtlv.com', '1592238018', 'https://www.caferio.com/locations/eastern', 'http://www.skysalon.com', None, 'http://www.tourneau.com/custserv/locate_store.cmd?storeNumber=33', 'https://www.bootbarn.com', '1592238033', 'http://www.modelcitizentoronto.com/', 'http://www.epiphanychandler.org', 'http://www.trueblueautomotive.com/', 'https://www.anatomica.ca', 'http://churchschicken.ca', 'http://facialsbysofia.com', None, 'http://www.davidesbakeryandcafe.com/', 'http://www.calgarygold.ca', 'http://www.laroccaspizzeria.com', 'http://www.rowhousecinema.com', 'http://www.buddhapie.ca', '1592238062', '1592238065', 'http://www.sunshinegrandcanyon.com', 'http://www.handysacehardware.com', 'http://www.honeybutterbakery.com/', None, 'http://carrepairvegas.com', 'http://www.tortoiseandharesports.com', None, None, 'http://www.buyerschoicelv.com/', None, None, 'http://www.erieislandcoffee.com', 'http://www.baytowne.net', 'https://www.sephora.com/happening/stores/gilbert-san-tan-village', None, '1592238099', 'http://www.glendaleca.gov/', 'http://www.youreliteplumber.com/', 'http://bestimpressionscaterers.com/main.php', None, None, None, None, None, 'http://www.newvisionaz.org', 'https://www.publicstorage.com/nevada/self-storage-las-vegas-nv/89146-self-storage/1477?pid=wyelp&CID=1245&CHID=AFL', None, None, 'http://larmco-oh.com', 'http://www.maisonettedistillery.ca', None, 'http://www.colonandrectalclinic.com', 'http://www.sirpizzafranklinpark.com', 'https://www.t-mobile.com/store-locator/nv/henderson/galleria-at-sunset-mall?cmpid=WTR_SE_YXT_U98MLWB9027148', 'http://www.dressbarn.com', 'http://www.choicehotels.com/en/choice-privileges', None, 'http://lrcorralescatering.weebly.com/', 'https://www.floxondanforth.com', None, 'https://dresspeopleltd.com/', None, 'http://Leonscaribbean.com', None, 'https://www.zippssportsgrills.com', 'http://www.clancyspubscottsdale.com/', 'http://www.alimentarimadison.com', None, None, 'http://www.atlashomeinspections.com', None, 'http://zinicolaitalian.com', 'http://www.sunsetclubcharlotte.com/', 'http://www.airspecialiste.com/', 'http://www.deltaco.com', 'http://www.wincofoods.com/', 'http://www.DFgym.com', 'https://www.smilesbysmith.com', 'http://www.drbahmanguyuron.com', 'http://salonstudiowest.com', None, '1592238192', None, 'http://royaldutchgrooming.net', 'http://www.dentistsonbloor.ca/', 'http://www.presidentspizza.com', 'https://www.bestwestern.com/en_US/book/hotel-rooms.03133.html?iata=00171910&ssob=BLBWI0005G&cid=BLBWI0005G:yelp:businessurl:03133', 'http://www.scottsdaledentalcare.net', None, 'http://www.nailsforyou.ca', 'http://www.zumiez.com', None, 'http://www.expressgaragedoorservice.com', 'http://acebroslv.com', 'http://www.tacarbon.com', 'https://www.onemainfinancial.com/branches/PA/Pittsburgh/15234/4721', 'http://www.starkmans.com', 'https://preciousmetalsnv.com', 'https://www.extraholidays.com/las-vegas-nevada/worldmark-las-vegas-spencer-street?lid=yelp&utm_medium=referral-affiliate&utm_source=yelp.com&Identifier=yelp&hotelid=103712&utm_campaign=localpage-worldmarklasvegas-spencer&promoid=localpage-worldmarklasvegas-spencer', None, 'https://www.lovestbrides.com', 'http://www.sakunthaionline.com/', 'http://www.gocomtrans.com', 'http://www.sanremobakery.com/', 'https://piedmontmaids.com/local-house-cleaning/nc/monroe', 'http://www.fluidmotionpgh.com', 'http://www.blisscupcakes.com/', None, 'http://www.tanprousa.com', None, 'http://www.rebekhasushi.com', 'http://www.crispfoods.com', 'http://www.usps.com', 'http://www.lvmpd.com', None, None, None, 'http://www.park2go.ca', 'http://www.horstmancomputers.com', None, 'https://www.walmart.ca/en/whitby-supercentre/3113', None, 'http://colosseumtraining.com', 'https://www.kindercare.com/our-centers/phoenix/az/000477?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=000477', 'http://clickserve.dartsearch.net/link/click?lid=43700044280216206&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'http://www.anytimedent.com', None, 'https://www.westelm.com', 'http://www.grayhawkbeerco.com', 'http://www.nextcare.com/locations/az/phoenix-thomas/?utm_source=Yelp&utm_medium=Local&utm_campaign=phoenix_thomas', 'http://goclarendon.com/restaurant', None, None, None, 'http://www.quiktrip.com', 'http://charliepalmersteak.com/locations/las-vegas', 'https://www.sprouts.com/store/az/laveen/laveen//?utm_campaign=website&utm_medium=listing&utm_source=yelp', 'http://www.thomasharman.com?cmpid=czhr_blm_0006', None, 'https://www.autoactionaz.com/dealership-locator/locations-1909-west-van-buren-street-phoenix-az/', 'http://www.ridgecleaners.com', 'http://www.plantworks.com', '1592238330', 'http://www.powerhouseplatinum.com/', 'https://thefortunatefox.com', 'http://www.ghazale.ca/', 'http://www.outback.com/locations/nv/las-vegas-craig', None, 'http://www.boom973.com/index.aspx', 'http://www.maac.com/texas/dallas/colonial-grand-at-hebron?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', 'http://ArizonaSailingAdventures.com', None, 'https://myhearingcenters.com/locations/nevada/summerlin', None, None, 'http://www.wellerracing.com/', 'http://www.timhortons.com', 'https://local.fedex.com/nc/pineville/PNVA/?cmp=LOC-1001545-3-2-971-1110000-US-US-EN-YEXTLISTFEDEXSC', 'http://primmed.org', None, 'https://www.cleanjuice.com/menu/', 'http://www.innovativehclinic.com', 'http://www.quickchangeoil.com/', 'http://www.azmortgagebrothers.com', 'https://valleywisehealth.org/locations/community-health-center-el-mirage/', 'https://www.menswearhouse.com/store-locator/2504?utm_source=yelp&utm_medium=listing&utm_content=2504&utm_campaign=AZ', 'http://www.liveatavanteapts.com', 'https://www.staples.com', 'http://www.northamerican.com/?refcode=844-434-1236&utm_source=yelp&utm_campaign=desktop', None, 'http://99only.com/store/Las-Vegas---Beltway/', 'https://theresortatsummerlin.com/dining/casual-dining/market-place-buffet-las-vegas/', 'https://www.jph4ever.com', None, 'http://www.imsaz.com', 'http://www.afabaz.com', None, 'http://www.perfectlookhairbraiding.com', 'http://www.regissalons.com/salondetail/default.asp?salonid=448', 'http://armor-plumbing-boiler.com/index.php', 'http://www.greatwraps.com', 'http://www.steepery.com/', 'http://nailsqueentoronto.ca', None, 'http://www.rodneysbybay.com', None, None, 'http://www.fitnesspropelled.com/', 'http://www.hawksbar.com', None, None, 'http://www.shakeitupbartending.com', 'http://www.salts-of-the-earth.com', None, None, 'http://store-locator.barnesandnoble.com/store/2039', 'http://www.vbflv.org', 'http://www.outlettags.com', 'http://www.702wingspot.com/', 'http://www.kitchenconnectionllc.com', 'http://www.lvparking.com', 'http://www.radair.com/', None, None, None, 'http://magroclothing.com', 'http://www.furnituretoronto.com', None, None, 'http://www.k2elec.com/', 'http://www.delanolasvegas.com/pool/delano-beach-club.aspx', 'http://woksupreme.com/', 'http://www.markandterri.com', 'http://www.goodlifefitness.com/locations/ontario/vaughan/milani-blvd?source=yelp-websitelink-vaughanmilani-gl', 'http://www.thegreatsteak.com/stores/7525', 'http://www.newdragonexpress.com/', 'http://www.daalroti.ca/', None, None, 'http://www.yourstarpupil.com', 'https://www.mccarran.com/Fly/WhichTerminal.aspx', 'http://www.lasvegascounselingcenter.com', None, None, 'http://www.glastek.com', '1592238519', None, None, 'http://www.burlingtoncoatfactory.com', '1592238526', 'https://www.galleriamc.com', 'https://www.tcclinic.com', 'https://www.midas.com/phoenix/store.aspx?shopnum=1109&dmanum=684001', 'http://az.scottsdale.charmingcharlie.com/fashion_accessories_scottsdale_az_45.html', 'http://www.shell.com', 'http://www.lapetite.com/your-local-school/monona-wi-7148/?utm_source=yelp&utm_medium=paid-directory&utm_campaign=enhanced-listing', None, 'https://www.jabzboxing.com/locations/32ndandshea/', None, 'http://www.tipsetreats.com', None, 'http://www.timhortons.com', 'http://www.amazingphotocamera.com/', None, 'http://www.waddellslonghorncorral.com/', 'http://www.desertsplashadventures.com', 'http://suburban-sanitation.com', None, None, None, 'http://www.thegilcreaseorchard.org', None, None, 'http://www.yasisplace.ca', None, 'http://philhousegrill.com', '1592238583', 'http://www.opticcreations.com/', 'http://www.trainingrevelations.com', None, 'http://www.statclinix.com', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, '1592238598', 'http://locations.daltile.com/az/tempe/118', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, '1592238610', 'http://www.josephsfoodandcakes.com', None, 'http://www.rowdyhair.com', 'http://www.starbucks.com/', 'http://jackastors.com/location-map/18/', None, 'https://www.choicehotels.com/ohio/wickliffe/econo-lodge-hotels/oh335/rates', None, 'http://www.blondesalon.ca', None, 'https://www.papajohns.com/international', 'http://luv2play.com/surprise/', 'http://independenceplumbing.net', 'https://pawn1st.net/our-locations/pawn1st-surprise-arizona/', None, 'http://www.lasvegasprostho.com', 'http://www.isshoniramen.com', None, 'http://www.eatatnakama.com', 'http://www.macklems.com/', '1592238663', 'http://www.towerofjewels.com/', 'https://stores.dickssportinggoods.com/oh/aurora/121/', 'http://www.lomography.ca', 'https://bostonpizza.com/fr/locations/st-bruno.html', None, 'https://www.kindercare.com/our-centers/goodyear/az/301663?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=301663', None, 'http://www.tinytooth.com', 'https://custommufflersaz.com', None, 'http://www.hairsmith.co', 'http://www.medicineshoppe.com/pharmacy-locations/pennsylvania/mt-washington/home', 'http://www.virgoesthetics.com', 'http://fawnboutique.ca/', 'http://www.btrustsupermarket.com/', None, None, 'http://www.allhoursplumbinginc.com', 'http://www.pridemgmt.com', 'https://thrifty.com/loc/ll/CA/OT/TORONTO-~-DANFORTH-(OT)/1245-DANFORTH-AVE', 'https://www.wisconsinrvworld.com', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.sfnevada.com?cmpid=UN7I_BLM_0006', None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://www.shibuyala.com', 'http://www.bell.ca/internet', '1592238730', None, None, 'http://www.deltaco.com', 'http://www.pizzapizza.com', 'https://habanerofreshmex.com', 'http://www.golfanything.com', None, 'https://la-coppa.com', 'https://www.montanas.ca', '1592238753', 'https://www.rallyhouse.com/rally-house-parma', 'http://balloonscharlotte.com', 'http://tton10.wix.com/pizanocustomautobody', 'http://www.secondcup.com/location/toronto-355-danforth-avenue', 'http://www.mmpguns.com', None, 'http://www.hair-dosalon.com', 'http://www.oxfordcleanersaz.com', None, 'http://hookahlounge.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=7781&localechange=1', 'http://www.silverstatevapor.com', None, 'http://www.sessionstattoo.com', '1592238788', None, None, None, 'http://wokintercuisine.com', 'http://sushi-ten.com/', None, None, 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=2179&localechange=1', 'http://madisoncircusspace.com', None, None, 'https://myhoneybakedstore.com/charlotte/114', 'https://wexford.orangetheoryfitness.com/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', None, None, None, None, 'http://www.marshallsonline.com', 'http://www.tiashortys.com', 'http://www.mariscosacapulco.org/Mariscos_Acapulco/Inicio.html', 'https://cmwireless.com', None, None, None, None, 'http://thelocalbarberandshop.com', None, 'http://www.mcgrathcpa.net', 'http://www.northranchvet.com/', 'http://www.unosalonlv.com', 'http://michelsbakerycafe.com/?q=node/1/en/', 'https://www.ebgames.ca/', 'http://www.drivesafeaz.net', 'http://www.journeys.com', 'https://www.engagestudio.com', None, 'http://www.azcostumeshop.com/', 'http://www.painsetsaveurs.com/', 'http://www.extraordinarytoys.com', 'https://www.dairyqueen.com/ca-en/Locator/Detail/?store-id=12605&localechange=1', None, 'http://www.fabricland.ca', None, 'http://www.quiktrip.com/', 'http://www.ahwatukeehoa.com', None, 'http://chase.com', None, 'http://Butlerfamilydentalaz.com', None, None, 'http://www.haydenelectricinc.com', 'http://www.parmatireservice.net', 'http://www.marcos.com', None, 'https://www.eliterooterphoenix.com', None, None, 'http://www.ilovepokebar.com', 'http://sushi-mori.ca', 'https://www.propertymanagementscottsdaleaz.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.jnphoenixfamilylawyer.com', 'https://www.vans.com', 'http://www.rowefarms.ca', 'https://www.sephora.com/happening/stores/hillcrest', None, None, 'https://www.cubesmart.com/nevada-self-storage/las-vegas-self-storage/90.html?utm_source=yelp&utm_medium=seo&utm_campaign=yelp-test-bp', 'https://shakeshakeseafood.com/contact_monroe', 'http://www.montessorivisions.com', None, None, None, 'http://www.MarshProperties.com', 'http://www.setispolishboys.biz', 'http://www.ctuckerandassociates.com', 'https://www.everbrookacademy.com/our-schools/charlotte-nc-4608/?utm_campaign=enhanced-listing&utm_medium=paid-directory&utm_source=yelp', None, 'http://www.costco.ca/', 'http://www.azdermacare.com/', 'http://www.yumbudz.ca', 'https://theeggworks.com', 'http://www.forgetaboutitsupperclub.ca', 'http://www.lbcexpress.com', None, 'https://www.reflectionzdetail.com', 'http://link.hertz.com/link.html?LinkType=HZLK&TargetType=Homepage&id=46190', 'http://www.lebelandcrowe.com', 'http://www.greencleanerslv.com', 'https://drgeoffreysherivf.com', 'http://www.beadworksjo.com', 'http://www.craigscustomupholstery.com', 'https://www.walmart.com/store/5066/avon-oh/details', None, None, 'http://www.philotavern.com/', 'http://www.abercrombiekids.ca/', None, 'http://www.jessieraesbbq.com', 'http://www.vetemergency.ca', 'http://www.carolinadoughnuts.com', '1592239007', 'http://www.starbucks.com', 'http://www.thespainthehollow.com/', '1592239015', 'http://www.bestclean-llc.com/', 'http://galenaeuropeanspa.com', 'https://www.kidsquest.com/location/boulder/', 'http://www.vsschnitzelhouse.com', None, None, 'http://www.fluidconcepts.net', 'https://www.myfitfoods.com/', 'http://kathysalterations.biz', None, 'https://www.cvs.com/store-locator/cvs-pharmacy-address/16545+East+Palisades+Boulevard-Fountain+Hills-AZ-85268/storeid=9279?cid=ps_ylp_2020', 'http://reflectionsautodetailing.me', None, 'http://www.thecannerygrill.com', None, None, None, 'http://www.paintboy.com/', '1592239059', None, None, 'http://arizonawindowwashers.com', 'http://www.courtyardatencanto.com/', 'https://titanicaz.com', None, 'http://labayoucasino.tumblr.com/', None, 'http://www.sapporoscottsdale.com', None, None, 'http://kappatoys.com', 'http://www.shoelabworld.com', 'http://www.goodwillaz.org', 'http://bk.com/', 'http://www.soldentalaz.com', 'http://www.lasvegaskidsrkids.com', 'http://www.caninecountry.ca/', 'https://www.halibuthouse.ca/locations/halibuthouse560mulockdrive/', 'http://www.pinoyscoffeeandboba.com', 'http://cp.cuyahogacounty.us/internet/index.aspx', None, 'http://www.airdrieautotrends.com/', 'http://www.leonesflorist.com', 'http://www.wavescoffee.com', 'http://viennamarketbroadway.com', None, 'http://www.desertskysurfaces.com/', None, 'http://www.chinachilirestaurant.com', 'http://www.bethanychristianschool.org', 'http://www.mazonac.com', 'http://stores.dickssportinggoods.com/az/mesa/725/', 'http://charlottefiberglass.com', None, 'http://www.chinapalacesewickleypa.com/', 'http://www.aceaxethrowing.com', 'http://www.exlacademy.com', 'http://www.deltastore.com', 'http://www.desertsunpt.com', 'https://bloomingnails-nailsalon.business.site', 'http://www.caremd.com/', 'http://giovanniandcompany.com/', None, None, 'http://www.razzles.biz/', None, None, None, 'http://www.dollartreecanada.com', 'http://www.socialsolutionsaz.com', 'http://www.springdayspa.com', None, 'http://www.bbkingclubs.com/', 'http://haciendasolanoresort.com', 'http://www.xperiencevapes.com', 'http://www.leakpoint.com', 'https://www.abccollisionrepair.com/?utm_source=yelp&utm_medium=listing&utm_campaign=yelp-business-listing', 'https://stores.loft.com/us/pa/homestead/126-west-bridge-street.html', None, None, 'http://eosfitness.com/location/tempe?utm_campaign=tempe&utm_medium=display&utm_source=yelp&utm_content=7-day-pass', None, None, '1592239206', None, 'https://dealer.sprint.com/experts-choice', 'http://local.biglots.com/oh/stow/453', 'http://www.yayaspizza.com/', 'http://www.portioncontrolnv.com', None, '1592239219', 'http://www.usmgcorp.com', None, None, 'https://www.boydautobody.com/locations/calgary-1st-st-ab', 'http://www.tranquil-lily.com', 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'https://www.aireserv.com/north-valley', None, 'http://www.bluerosepottery.com', None, 'https://locations.panerabread.com/oh/highland-heights/6345-wilson-mills-road.html?utm_medium=display-ad&utm_source=paid-digital&utm_campaign=yext&utm_content=local-search', 'http://www.retroburger.ca/', 'http://crunchbistro.com', 'http://www.valuevillage.com', 'http://www.bleedingrosetattoo.com', None, None, None, 'https://www.goodyearautoservice.com/en-US/shop/AZ/Glendale/000908234-85308-2429', 'http://www.lisboabakeryanddeli.com', None, None, 'http://www.swingpgh.com/', 'http://www.daydreamsdropin.com', 'http://valleypoolcleaning.com/', None, None, 'http://www.vaultnc.com/', 'http://www.tonicsalonnv.com/', '1592239283', 'https://airpromaster.com', 'http://www.queencityautosalesnc.com', 'http://pageperpage.com', None, 'https://www.firehousesubs.com/locations/oh/willoughby-commons', '1592239298', None, 'http://laptoprepairs.com', None, None, 'http://www.lashliqueur.com', 'http://www.airportgatecafe.com/', 'http://www.naturallyyours.ca', 'http://www.shopkkbloom.com', 'http://www.honestyelectricllc.com', None, 'http://www.husd.org', 'http://www.ucalgaryrecreation.ca', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.exacttemphvac.com', None, None, 'http://www.madisonorientalwok.com', 'http://www.crossfitarchangel.com', None, 'http://www.jolieannephotography.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'http://www.rockabettyssalon.com/', 'http://c2cnd.org', 'http://www.fantasticsams.com/', None, 'http://www.gamestop.com', 'https://www.safelite.com', 'http://cleanenvision.com', 'http://www.ahugheshairdesign.com', None, 'http://www.filibertos.com', 'http://www.kmjwebdesign.com', None, 'http://www.dillysdeli.com/', None, 'http://www.kimchikoreahouse.ca/', None, None, 'http://www.mississauga.ca/portal/discover/parksandgardens?paf_gear_id=9700018&itemId=300019', 'https://www.publicstorage.com/arizona/self-storage-mesa-az/85210-self-storage/787?pid=wyelp&CID=1245&CHID=AFL', '1592239382', 'http://www.teavasee.com/', 'http://www.popularpizza.ca/', None, 'http://www.steffiblackcoaching.com', 'http://www.virginiajohnson.com', 'http://www.kindercollege.ca', None, 'http://www.toysrus.com/family/index.jsp?categoryId=2255956&camp=MISC:yelp:store:page:tru:111910', 'http://www.gdpeds.com/', 'http://www.coldwaterspringsapts.com/', 'http://www.eyecarecenter.com/optometrist-locations/matthews-mint-hill-rd/?address=28105', 'http://www.minus5experience.com/', None, None, 'http://premiercleaners.com', None, 'http://www.theherbcard.com', None, None, 'http://www.maac.com/north-carolina/charlotte/post-ballantyne?utm_medium=cpc&utm_source=yelp&utm_campaign=2019', None, None, 'https://www.unlv.edu/dental', 'https://www.thestonecollection.com/phoenix', 'http://www.sweetpetes.com', None, 'https://www.aaautocarelv.com/locations/decatur-blvd/', None, 'http://www.allnationsdriving.ca', 'http://icehousebrooklyn.com/', 'http://www.carusogourmetpizza.com/', None, None, 'http://www.sparrshspa.com', None, 'https://www.mezzo1.com/?utm_source=yelp', 'http://www.jimtuckerroofing.com', 'https://www.redmountainweightloss.com/ahwatukee/', None, 'http://www.jackinthebox.com/', None, 'http://www.thebeautyloftaz.com', 'http://www.papadelspizza.com/', 'https://www.maricopa.edu', None, None, 'https://www.lasereyecenteraz.com/eye-doctors/kianoush-kian-m-d/', 'http://www.Altus-HPO.com', 'http://yourspacesalons.ca/natural-solutions', None, None, None, 'http://www.buckle.com', 'https://locations.wendys.com/united-states/nc/charlotte/7920-cambridge-commons-drive', 'https://www.glassdoctor.com/phoenix', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=1131', 'http://goodfoodmadison.com', None, None, 'http://www.suicidejims.com', None, None, 'http://www.thelaughshopcalgary.com', None, 'http://www.skyzone.com/phoenix', None, None, 'http://www.animalcareclinicinc.com/henderson-animal-hospital', None, 'http://www.center-towing.com', 'http://www.regency.edu/campus/north-olmsted-ohio.aspx', 'https://www.purdys.com/shops/details/79', 'http://www.hottopic.com', 'http://www.carolinatotalcare.com', None, 'https://locations.jackinthebox.com/us/nv/las-vegas/1591-s-main-st', 'http://archstonecare.com/', 'http://www.kibosushi.com', 'http://rulysauto.com', None, 'https://www.earthfare.com/stores/', 'http://www.allapplianceneo.com', 'http://denver.unique-accounting.com', None, 'https://www.wyndhamhotels.com/hotel/33877?tel=18003291073&iata=00093785&cid=fe:di:20161220:yl:pp:dius:33877', None, 'https://vansoncuisine.ca', 'http://www.donsappliances.com', 'http://alphillipslv.com/', '1592239567', 'http://www.larrystow.com', 'https://www.marleneharriscol.com', 'http://www.consonantskincare.com', None, 'https://www.tgifridays.com/locations/1742/fridays-charlotteuniversity-north-carolina', 'https://locations.eatandys.com/ll/US/NC/Concord/8835-Christenbury-Pkwy', 'http://jmacvideo.com', 'http://www.aosmlv.com', 'http://enticare.com', 'http://www.marriott.com/hotels/travel/pitmv-springhill-suites-pittsburgh-monroeville/?scid=bb1a189a-fec3-4d19-a255-54ba596febe2', 'http://www.theciderfarm.com', 'https://www.presslyanimalhospital.net', None, 'http://www.remax.com/realestateagentoffice/lasvegas-nv-89128-sandrathomas-id11154472.html', 'http://www.meadowlarkestables.com/', 'http://www.salon-atmosphere.com/', 'http://chicagobrewinglv.com', None, None, None, 'http://www.mrlube.com/en/Mr-Lube-Near-You/Locate-a-Mr-Lube/mississauga-2191-dundas-street-e.aspx', 'http://www.doitbest.com', 'http://sterlingssteakhouse.ca', 'http://www.saloncollage.com', 'http://www.eatatbobsdiner.com/', 'http://www.kamasutrarestaurant.ca', 'http://www.swisschalet.com', 'http://www.dunkindonuts.com', None, 'http://locations.atipt.com/grayhawk-scottsdale-az', 'http://www.magicvaporllc.com', 'http://www.starbucks.com', 'http://www.AllBreedMadison.com', 'http://www.montanameatco.com', 'http://bk.com/', 'http://www.starbucks.ca', None, 'http://www.autobell.com/ab_locations/750-n-church-st/', None, None, 'http://www.marriott.com/hotels/travel/cleta-towneplace-suites-cleveland-airport', None, None, None, 'http://workoutanytime.com/charlottewest', 'http://carolinasmiledesignsc.com', 'https://depotbarbershop.business.site/?m=true', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', '1592239672', 'http://www.libertyiron.com', 'http://aaffordablebabysitting.com', 'http://www.quesada.ca', 'http://bk.com/', 'https://locations.theupsstore.com/wi/sun-prairie/1223-w-main-st?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'http://www.kay.com', 'https://www.ugg.com/stores/s/fashion-show-mall?latitude=36.127172&exclude=18231&page=1&longitude=-115.171661&storesPerPage=3', 'http://www.creolecajunbistro.com', None, None, None, 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpsoutheastorganic', 'http://www.wolfcamera.com', 'http://www.corygoldbergmd.com/', 'http://www.harborfreight.com', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.paksweets.com', 'http://www.airpads.com', None, 'http://www.norterrafamilymedicine.com', None, 'http://www.kensingtonbrewingcompany.com', 'http://25chiropractic.com/', '1592239728', 'http://coffeedaklak.com', None, None, 'http://freddyrguez.googlepages.com/', 'https://www.crossborderpickups.ca', 'http://www.dilworthbilliards.com/', None, 'http://www.ahghomewarranty.com', None, None, '1592239754', 'http://www.guggenheimhermlasvegas.org', 'http://www.pearl-factory.com', None, 'https://local.biglots.com/pa/pittsburgh/1478?zcp=pd_local_yelp', 'https://www.navyfederal.org/?cmpid=bn%7Cyelp%7Cevgrn%7Cbrn%7Cnull%7Cnull%7C01/13/2020%7Cml%7Cnull', 'http://www.sallybeauty.com', 'http://www.salonfair.com', 'https://sunvek.com', 'http://www.midas.com/calgary/store.aspx?shopnum=9304&dmanum=151', 'http://www.bakersbookkeeping.com', None, 'https://phoenix.swimspas.us', None, 'http://torontopremiumoutlets.ca/outlet/toronto', 'http://www.midwifeskaleidoscope.org', 'http://www.redrockfencingcenter.com', 'http://www.azairworks.com/', 'http://auraapts.com', None, 'http://www.discountroofingnv.com', 'http://www.drvinyl.com', 'http://www.newskyrestaurant.ca', None, 'http://www.portauthority.org', 'http://www.downtownbrewfestival.com', None, 'http://www.globallylocal.ca', 'http://www.kakabeautyspa.ca', None, 'http://www.noelinwheeler.tattoo', 'http://concourseroffler.blogspot.com', 'http://www.rexall.ca/', 'http://www.trailsidetreasures.com', 'http://www.nevadatirecity.com', 'http://www.cornerstonewomenscare.com', 'http://www.easyhome.us', 'http://www.mondashaircare.com', 'https://www.desertfinancial.com/Home/BranchDetails?branchId=1', 'http://newks.com', 'http://www.dcspoolbarriers.com', 'http://www.drrochlin.com', 'https://www.fit4less.ca/locations/alberta/calgary/408?utm_source=yelp&utm_medium=cta&utm_term=calgarymacleod-f4l', 'http://www.julietlefleur.com', 'http://www.arizonahairco.com/', 'http://www.dunkindonuts.com', 'http://montana-hookah-longue-and-smokeshop.business.site', 'http://miniso.ca', 'http://www.westairaviation.com', 'https://www.sunrisepreschools.com/locations/baseline-gilbert/?utm_source=yelp&utm_campaign=online_listing_gilbert_280&utm_medium=referral&utm_term=business_url', 'http://www.mackdentistry.com/', 'http://thayersselectmeats.com', 'http://undergrounddiesels.com', '1592239872', 'http://www.samuraicomics.com', '1592239878', 'http://www.michaelkors.com/stores/united-states/nv/las-vegas/michael-kors-palazzo', 'http://willytechshop.com', 'http://www.vernspizza.com', 'http://www.clearviewinstitute.com/', 'http://www.berkeleyplace-apts.com', '1592239893', None, None, 'https://venecia-beauty.business.site', 'http://www.haircutmenriverbendcalgaryab.ca', 'https://www.hungryhowies.com/store/hungry-howies-01805?utm_source=Yelp&utm_medium=Referral&utm_campaign=Yelp_CTA&utm_term=01805&utm_content=Website_Link', 'https://sophiaslounge.com', 'http://www.taxicabchandler.com', 'http://www.bestchickenwings.com/', 'http://www.athletico.com/locations/tempe/?utm_campaign=yelp-listing&utm_medium=web&utm_source=yelp-tempe', 'http://www.solsticerestaurant.ca/', 'http://www.azclubluxx.com', 'http://www.sethkoreytennis.com', None, None, 'http://www.flairtrade.ca', None, None, None, 'http://www.vegasmartialarts.com', 'http://riobel.ca', None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, None, None, None, 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', 'http://www.hairea51.net', 'http://www.dmvdrop.com', 'http://carolklemp.wix.com/aefitness', 'http://www.3Brewers.ca', 'http://www.lisaturley.com', 'http://oldtownweddingcenter.com/', None, None, None, None, None, 'https://zoomrentals.com/toronto-airport-car-rentals', 'http://www.rehabplusscottsdale.com', 'http://azdirectmobility.com', 'http://www.torpedocomics.com', None, 'https://www.aladdinswindowtinting.com', None, None, 'https://www.ewingirrigation.com', None, None, None, '1592239999', 'http://www.dapaulsalon.com', None, 'http://productnightclub.com', 'http://desertmesapool.com', None, 'http://www.cltchristmasvillage.com', None, '1592240015', 'http://www.animalhospitalhighpark.com/', 'https://bhrcenter.com/location/boca-park-nv/', 'http://www.conns.com/store-locator/arizona/scottsdale-85250', None, None, None, 'http://www.bestfootspascottsdale.com/', 'http://elitepetcare.com/', 'http://www.reservesquareapts.com', 'http://www.livelovelashe.ca', 'http://www.ibrandyourbusiness.com', 'http://wingsonbroadway.com/', 'https://mugshotzofficial.wixsite.com/mugshotz', 'https://www.luckysmarket.com', 'http://linkfinancialadvisory.com', 'https://www.gocleancredit.com', 'http://www.rothmanawningco.com/', 'http://www.fredastaire.com/scottsdale', 'http://www.sweettomatoes.com', None, None, 'http://www.bellairconditioningaz.com', None, 'http://www.arbys.com', None, 'http://tempeautorepairshop.com', None, 'http://martinjlevinedds.com/', '1592240069', 'http://www.carolinaurology.com', 'http://www.whiteningxpressions.com', 'http://www.chevron.com/', None, 'http://www.jambajuice.com', 'https://www.honorhealth.com/locations/hospitals/scottsdale-thompson-peak-medical-center?utm_source=yelp&utm_medium=local&utm_campaign=Scottsdale_Thompson_Peak_Medical_Center', '1592240085', 'https://locations.wafflehouse.com/nc-pineville-1157', None, 'http://www.lasvegasapartments-r-us.com/Mirabella-Apartments-for-Rent-in-Las-Vegas.html', '1592240094', 'https://www.supercuts.com/locations/nv/las-vegas/parkway-retail-center-haircuts-82614.html', 'https://www.waterstreetpizzeria.com', 'https://familymoversexpress.com', None, None, None, None, None, None, 'https://www.mcdonalds.com/us/en-us/restaurant-locator.html?cid=RF:Yelp:::RODBOGONov', 'http://www.asphaltpavingranaldi.com', 'https://locations.jackinthebox.com/us/az/peoria/8236-w-deer-valley-rd', 'http://www.tjmaxx.com', None, None, 'http://www.swarovski.com/en-US/?utm_source=YELP&utm_medium=referral_managed&utm_campaign=YELP', 'http://www.chiefdodge.com/', 'https://www.titlenine.com/store-locator/title+nine+-+madison.do', 'http://www.tiremanusa.com/locations.aspx', None, 'http://www.wolfsonmedicalcenter.com', 'http://greenwayfamilyautoandtowing.com', 'https://www.orangetheory.com/en-us/locations/arizona/peoria/25314-n-lake-pleasant-pkwy-suite-1260/?utm_source=redirect&utm_medium=print&utm_campaign=yelp&utm_term=032016&utm_content=yelp_print', 'http://www.woodysdogbath.com', 'http://www.mayfieldbrainard.com', None, None, 'http://www.scrubsandbeyond.com', 'http://fitnessfactorycharlotte.com/', 'http://azsportsmedicine.com', 'http://www.idealservices.com', None, None, None, 'https://www.brasstapbeerbar.com/Charlotte', 'http://www.seaminglystraight.com', None, 'http://www.whitfillnursery.com', None, 'http://www.chip-n-daleslandscaping.com', 'http://www.illinitechcenter.com', None, None, 'http://www.villageicecream.com', '1592240192', None, 'http://www.carpet-cleaning-pittsburgh.com', 'http://www.thelowcarbgrocery.com', 'http://lezah.ca', 'https://www.brakesplus.com', 'http://paulmitchell.edu/phoenix', None, None, None, None, 'http://www.alohabbqgrill.com', 'https://www.esso.ca/en/gas-station/etobicoke-on-geesso-200302279', 'http://www.edencafelounge.ca', 'http://www.signsbytomorrow.com/mesa/', 'http://www.borders.com', None, None, 'https://locations.theupsstore.com/nv/las-vegas/840-s-rancho-dr?utm_campaign=Listings&utm_medium=organic&utm_source=Yext', 'https://peoriafootandanklespecialists.com', None, 'http://tshirtdinervegas.com', None, None, '1592240240', 'http://lebistrodubeaujolais.com/', 'http://farmershouse.ca', 'http://www.sarkujapan.com/', None, None, 'http://www.charlotterusse.com', None, 'http://kpiteophotography.com/', 'http://www.aceshighpartyrental.com/', 'http://www.harveys.ca', 'https://www.walgreens.com/locator/walgreens-11001+s+eastern+ave-henderson-nv-89052/id=6545', 'https://www.altimadental.com/locations/first-canadian-place', 'http://www.rockcitytaphouse.com', 'http://www.thelucky20cafe.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/YYCSC', None, None, 'https://www.yeahyeahspizza.com/toronto', None, 'https://locations.panerabread.com/oh/parma/8109-w-ridgewood-dr.html', 'http://www.clearsound.co', 'http://www.sunrisecoffeelv.com', 'http://www.herbergertheater.org', None, None, 'https://pittsburghmoving.net', 'http://www.phoenixcakecompany.com', 'http://www.timothys.ca', 'http://www.olivetree-apartments.com', None, None, 'http://www.ltayh.com', 'https://www.walgreens.com/locator/walgreens-1745+e+southern+ave-tempe-az-85282/id=1197', 'http://dobsonranchdentalcare.com', None, 'http://www.elitedancestudiolv.com', 'http://www.boosterjuice.com', 'http://www.meckabc.com', 'https://www.realestatelawfirmphoenix.com', '1592240325', 'http://www.goodyearsfamilymedicine.com', 'http://www.drdanstrinkoski.com', 'https://www.petpeoplestores.com/avon-store.html', 'http://www.bedfordautocare.com', 'http://www.shininghopefarms.org/', None, 'http://www.freshandeasy.com/', 'http://www.csuohio.edu/artgallery', 'http://www.desertpalettepainting.com/', 'http://www.premierairsolutions.com', '1592240349', 'http://www.desertroselandscaping.com', '1592240354', 'https://locations.usbank.com/index/kentucky/henderson/old-orchard-branch.html?utm_source=yelp&utm_medium=business%20listing&utm_campaign=visit%20website', 'http://www.dmconcrete.biz', 'http://bluestardiner.ca/', None, 'https://sweetiepiescatering.com', 'https://www.azbouncepro.com', 'http://www.ritters.com', None, 'http://Arizonasoldsisters.com', 'http://www.restaurantdepot.com', 'http://pizzafire.com', 'https://www.ikea.com/us/en/stores/tempe/', None, 'http://www.regaloaksdental.com/', 'https://www.signaturestyle.com/locations/pa/penn-hills/borics-hair-care-penn-hills-shopping-center-haircuts-75141.html', 'http://99only.com/store/Las-Vegas---Beltway/', None, 'https://www.jovannalv.com', 'http://www.coppercanyondentalaz.com/', '1592240397', 'http://journeyeducation.org', None, 'http://www.tandyleatherfactory.com', None, None, None, 'https://local.fedex.com/nv/las-vegas/office-1441/', 'http://www.madameboeuf.com', 'https://www.fitzroyrentals.com', 'http://www.resumetarget.ca/location/ontario-on/toronto/', '1592240420', 'http://callnoworriesjanitorial.com', 'https://www.autozone.com/locations/in/avon/7474-e-us-36.html', None, 'https://www.zoup.com', 'http://www.thedistrictatgvr.com/alsGarage.php', 'http://www.kixs.ca', 'http://www.immigroup.com', 'http://www.burlingtoncoatfactory.com', None, None, None, 'http://www.swensensaz.com', None, 'http://www.arrowheadautocare.com', None, 'http://www.lucasautomotive.ca/', 'http://lululemon.com/toronto/queenstreet?cid=yelp', None, 'https://www.nothingbundtcakes.com/bakery/az/surprise?utm_source=yelp&utm_medium=brandedprofiles&utm_campaign=surprise_300', None, 'http://www.rnbflooring.com', 'http://www.fortpittblockhouse.com/', 'https://www.hilton.com/en/hotels/cltbahw-homewood-suites-charlotte-ballantyne-nc/?SEO_id=YELP-HW-CLTBAHW', 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', 'http://www.cortebellagolfclub.com', 'http://www.popsbarber.com', None, '1592240482', None, 'http://www.greenbeauty.ca', 'http://24hrlockoutsmadison.com/', 'https://kevindeon777.wixsite.com/remodel', 'https://www.needforsweetslv.com', 'http://suzieqluxe.com', None, 'http://www.torontoislandsup.com', None, 'http://www.azhumane.org', 'http://www.providenceprepschool.com/', '1592240510', 'http://kierlandresort.com/fine-dining-at-scottsdale-restaurants/scotch-library/', 'http://www.vocellipizza.com/mccandless_pa', 'http://shawarmaroyale.com', 'http://bullseyervrepair.com', None, None, 'https://www.westelm.com/stores/ca/on/toronto-shops-at-king-liberty/', 'http://www.sterlescountryhouse.com', 'http://www.dawgdayzcare.com/', 'http://www.superiortire.ca/locations/mode/4/3-laidlaw-blvd-markham-on-l3p1w5.aspx', 'https://experigreen.com/service-area/charlotte-nc/', 'http://www.michaelscateringevents.com', 'http://www.footdocvegas.com', 'http://www.InfinityAcuAZ.com', 'http://www.eggsmart.ca', 'http://www.cakestoyou.net', None, None, None, 'http://www.thecorneralley.com', 'http://www.pinkpetalsflorist.com', 'http://www.thecroftdowntown.com/', 'http://www.dbacks.com/', 'https://www.smilefitnessdentalcenter.com', 'https://stores.savers.com/nv/lasvegas/savers-thrift-store-1047.html', 'https://www.appliancepartscompany.com', 'https://www.marriott.com/setSCtracking.mi?scid=dfedf519-6161-4ae6-be84-577f767ed579&mid=/hotels/travel/CLTWS', None, 'http://www.MortgageAssociatesOntario.com', None, 'https://locations.rallys.com/oh/parma/6201-brookpark-road/?utm_source=Yelp', None, 'https://www.bestbuysoccer.com', 'http://www.aeropostale.com', 'http://www.alternativehealingconnection.com/', None, 'http://www.mastercleaningaz.com', 'http://www.thepoddrop.com', 'http://www.dozoaz.com/', 'http://luckysloungelv.com', 'http://www3.hilton.com/en/hotels/north-carolina/hilton-charlotte-center-city-CLTHHHF/index.html', 'http://bestofsevenbarbers.com/', 'http://www.lorispetagree.com', 'https://deltaco.com', 'http://firstwindfitness.com', 'https://lakehealth.org/Locations/TriPoint-Medical-Center', None, 'http://www.swisschalet.com', None, None, None, None, '1592240633', 'http://www.midaslocator.com/AutoRepairFinder/tabid/151/Default.aspx', 'http://www.pricklypeachwaxbar.com', None, 'http://asappoollv.com', 'http://www.snipits.com/locations/avon/', 'http://www.timhortons.com/', 'http://www.43north.biz', 'http://www.mixxmethod.com', 'http://www.rizegaragedoor.com', None, 'http://www.papagostables.com', None, None, None, 'http://theswedishconnection.net', 'https://www.bestwestern.com/en_US/book/hotel-rooms.66083.html?iata=00171890&ssob=BLBWI0003G&cid=BLBWI0003G:yext:website:66083', 'http://federicosmexicanfood.com', None, None, 'http://www.calvarychristiandaycare.com/', 'http://www.phxdj.com', None, 'https://www.ezwindowsolutions.com/cleveland/', 'http://www.mrappliance.com/pittsburgh', None, 'http://www.opsiseyecare.com', 'http://www.avanteoptics.com', None, 'https://www.chronicinktattoo.com/locations/tattoo-shop/chronic-ink-midtown-toronto-yonge-eglinton/', None, 'http://www.adaptiveforce.com', None, 'http://www.thecatnfiddlepub.com', 'http://www.valleyymca.org', 'http://www.ladybugpestcontrol.com/', None, None, '1592240712', None, 'http://www.greenfieldcitrus.com', 'http://www.prada.com', None, None, None, 'http://www.towncentredentalclinic.ca', 'http://www.hobbyhobby.com', None, 'https://southpointcasino.com/entertainment/grandview-lounge/?cid=ypgl', 'http://crystalclearreflectionsaz.com', 'http://danielacaltarumd.com/', None, 'http://www.cleantheworld.org/', 'https://www.famousfootwear.com/?partnerid=YELP', 'http://www.newhorizonlittlelearners.com', 'https://www.hairclub.com/locations/nv/las-vegas/hair-loss-clinic-292/?pub=loclisting&utm_source=yext&utm_medium=loclisting&utm_campaign=YX_292', 'http://galatimarketfresh.com', '1592240751', None, 'http://www.toysrus.ca', 'https://www.cvs.com/store-locator/cvs-pharmacy-address/9302+Olde+Eight+Road-Northfield+Center-OH-44067/storeid=4301?cid=ps_ylp_2020', None, 'http://www.salonritualsaveda.com', 'http://www.jetfuelcoffee.com', None, 'http://www.mrhero.com', 'http://www.lululemon.com/thornhill/promenade?cid=yelp', 'http://www.destinationweddingphotographycalgary.com', 'http://www.golfthebridges.com/barandgrill/', '1592240777', 'http://funtropolis.ca', 'http://www.bilmarcompanies.com', None, 'https://www.aznaturalselections.com', 'http://locksmith4Uvegas.com', 'http://scotiaplaza.kidsandcompany.com', None, '1592240796', 'http://www.greatclips.com', 'http://gremassagetherapy.com', 'http://www.fortunenails.ca', 'https://locations.massageenvy.com/arizona/peoria/10006-w-happy-valley-parkway.html', 'https://www.extraspace.com/storage/facilities/us/north_carolina/charlotte/1000000404/?cid=org::ld&utm_source=yelp&utm_medium=referral&utm_campaign=org::ld', 'http://www.kodisnaturalpetfoods.com', None, 'https://www.papamurphys.com/store-finder/position?utm_source=yelp&utm_medium=2018ads&utm_campaign=SC011', 'http://www.arizonahairco.com', None, None, 'http://www.desi.bar', None, 'http://mkt.com/mobile-bubbles', 'https://www.walmart.com/store/3473/las-vegas-nv/whats-new', None, 'https://www.pizzahut.ca/store-details/store-R31411/pizza-hut-Toronto', 'http://www.waborasushi.com/', 'http://salon7000.com/', None, None, 'http://www.whitecastle.com', None, None, None, '1592240855', None, None, '1592240862', None, None, 'http://www.averyonthegreen.com', None, 'https://www.southviewdentallv.com/index.php', None, None, 'http://www.firstcu.net', 'http://www.anytimegaragedoor.com/', 'https://sardellaspizza.com', None, 'http://www.panevinorestaurant.net/about.html', 'http://www.newhealthdentalaz.com/', None, 'http://www.hatleystore.com', 'http://xtremeairaz.com', 'https://www.phoenixconventioncenter.com/orpheum-theatre', None, 'http://www.veronadentalcare.com', 'http://www.canyonridge.org', 'http://mint-landscape-creations-llc.business.site', None, None, 'http://www.academyofsound.org', None, 'http://lowell.wisc.edu', None, None, 'http://www.chandlervisioncenter.com', None, 'http://www.sugarmarmalade.com', 'http://shoparooni.com', 'http://www.dieselbarbershop.com', 'http://www.allcitytransportation.com', None, 'http://premierdental702.com', 'http://www.dominos.com', 'http://www.lazylizardaz.com/', 'http://www.qqteaplus.com', 'http://snailmotorsports.com/', 'https://www.autozone.com/locations/az/phoenix/8325-w-camelback-rd.html', 'http://www.lacasalatina.net', 'http://www.itzzapizza.com', 'https://www.aritzia.com/en/store-locator?q=M9C+1B8&view=results', 'https://www.plannedparenthood.org/health-center/wisconsin/madison/53713/madison-south-health-center-3937-91860?utm_campaign=madison-south-health-center&utm_medium=referral&utm_source=yelp.com&utm_content=link', None, None, 'http://www.azkarateacademy.com', 'http://olivebranch412.com', None, None, 'http://susiesestateaz.com/estate_sales', None, None, 'http://www.thaiexpress.ca', 'https://www.advantagestorage.net/self-storage/az/phoenix/advantage-storage-moon-valley/', 'https://florist.1800flowers.com/us-nv/1-800-flowers-shoppe-las-vegas', 'http://www.weavebaratl.com', 'http://www.migrationlaw.com', 'http://www.iceburghs.com', 'http://www.drgreencerts.com', 'http://modernnailsandlash.com', 'https://recreationalartstudio.com', None, 'http://design-ramon.com', 'http://www.sallybeauty.com', 'http://www.just4funsportingclub.com/', 'https://www.pandaexpress.com/?utm_source=yelp&utm_medium=profile&utm_campaign=1378&utm_content=bpas', 'http://www.lush.ca', None, 'http://www.madsens.ca/', 'http://www.sportracks.com', None, 'https://www.fatburger.com/locations/rancho', 'http://www.azsuperiorhomeinspections.com', 'http://www.earnhardtcadillac.com/', None, '1592241033', 'http://barneyslounge.ga', 'http://brianwilliamsdds.com/', 'http://www.simplyflowerstoronto.com', None, 'http://www.arizonaautowashscottsdale.com', 'http://www.dunkindonuts.com', 'http://www.PattersonHomesAZ.com', None, 'http://www.outback.com/locations/oh/independence', 'https://pablocanada.com', None, 'http://www.mychiropractoraz.com', 'http://www.hollospapercraft.net/', 'https://www.searsauto.com/stores/6601?psid=campaigncode-6601', 'http://www.sayyestoherdress.com', None, 'http://www.eyestudio.ca', 'http://www.highlandfarms.ca', 'https://tendollarshirtstore.com', 'http://www.cineplex.com/Theatre/cineplex-odeon-eglinton-town-centre-cinemas', 'http://www.myhusky.ca/station_locator.html?provinceID=AB', 'http://peaksandrafters.com', 'http://www.junkmastersinc.com', None, 'https://www.filerchiropracticpittsburgh.com', 'http://www.westsidemarket.org/vendor.aspx?id=77', 'http://www.ttc.ca/Subway/Stations/St_Patrick/station.jsp', 'http://www.gzcomics.com/locale.html', 'http://www.deltaco.com', 'https://jade-chinese-kitchen.business.site', None, 'http://www.bojangles.com', 'http://Clocktowerbar.ca', 'http://valleyislepumping.com/', 'http://www.quiznos.ca', None, None, None, 'http://www.bigotires.com', None, 'http://stpaulpgh.org', 'http://coopersbbqco.com/', 'http://www.ecokingaz.com', None, None, 'http://www.powervac.ca/power-vac-toronto-gta', None, 'http://www.myphoenixair.com', 'https://www.gianteagle.com/Stores/Store/?storeId=6299', 'http://www.Team1stRealEstate.com', 'http://www.fickleonline.com', 'https://vcahospitals.com/bakerstown?utm_source=yelp.com&utm_medium=referral&utm_term=VCA_Bakerstown_Animal_Hospital=main_url', 'http://www.jglennhome.com', '1592241164', '1592241167', 'https://www.doggiedistrictaz.com?utm_source=yelp&utm_medium=social', None, None, 'http://changjiangbestmadison.com', 'https://www.theacteam.com', None, 'http://www.eatoooweebbq.com', 'http://fourcornersbakery.com', None, 'http://www.paintstoretoronto.com', 'https://stores.toysrus.com/az/goodyear/baby-store-goodyear-az-b5641.html', 'https://www.fiix.io', 'http://www.visualharmonyphotography.com/', 'https://landmarkautoanddiesel.com', 'https://www.lafitness.com/Pages/clubhome.aspx?clubid=830', 'https://finedetails.ca', 'http://www.tbdc.com', 'https://www.liveedgelust.com', 'https://www.kinjosushiandgrill.com', 'http://GrizzlyAC.com', 'http://www.opticausa.com', None, 'https://www.simonmed.com/locations/all/simonmed_imaging___sun_city_peoria', 'http://www.advancedhearinggroup.com', 'https://sacredpi.com', None, 'https://www.transformyourself.ca', None, 'http://clickserve.dartsearch.net/link/click?lid=43700044282967270&ds_s_kwgid=58700005061605699&ds_url_v=2&ds_dest_url=https://www.pizzahut.com', 'https://arirangkoreanbbq.business.site', 'http://www.marqueetheatreaz.com', None, 'http://peoriaartisanbrewing.com/tap-room/', 'http://www.holeechow.com', 'https://www.abcgaragedoor.biz', 'http://webersvintageicecream.com', None, 'http://www.leewiyoga.com', None, 'http://www.lucapizza.ca/', None, 'https://www.wangskitchenpa.com', 'http://northofbombay.com', 'http://www.eandrsweetery.com', 'http://indodesignerrugs.com', 'http://www.landmarkhomeserv.com', None, None, 'http://www.saharaautolv.com', 'http://www.drlizcruz.com', 'https://www.wingstop.com/location/wingstop-230-glendale-az-85306/menu', 'http://www.northcoastjawcenter.com', None, '1592241292', None, 'https://www.loblaws.ca/store-locator/Loblaws+-+St.+Clair+Ave+West/1212?storeId=1212', None, 'http://glassking.com', None, 'http://www.glamoursalonandspa.ca', None, 'http://www.CapstoneBrokerage.com', 'http://www.myrivertowne.com', 'http://www.hotrodpiercingcompany.com/index.html', 'http://www.tuckyshotdogs.com', None, 'http://www.getdynamicdetailing.com', None, 'https://www.sprouts.com/stores/details/-/store-details/view/store/20/?utm_source=yelp&utm_medium=listing&utm_campaign=website', 'https://www.walgreens.com/locator/walgreens-3945+e+southern+ave-phoenix-az-85040/id=4422', 'http://local.tiresplus.com/store/Madison-East?lw_cmp=YLP_TP_53714&utm_source=YLP&utm_medium=TP_53714', None, 'http://www1.shoppersdrugmart.ca/en/store-locator/store/359', None, 'http://www.theyardpgh.com/market-square', None, None, None, 'http://www.nissanairport.com', 'http://pilateselementlv.com', 'http://bodega13.com/', 'http://freedomclothingcollective.com', 'http://trackofficefurniture.com/', None, 'https://locations.visionworks.com/ll/US/PA/Pittsburgh/120-Fifth-Ave-Pl', 'http://www.healthree.ca', None, None, '1592241373', 'http://www.glamourco.com', 'http://www.goodlifefitness.com/locations/ontario/toronto/kingliberty?source=yelp-websitelink-torontoking-gl', 'http://www.rei.com/stores/paradise-valley.html', 'https://www.chipotle.com?utm_source=Yelp&utm_medium=Yelp-listing&utm_campaign=cmg_yelp_listings', None, 'http://www.cornerstone-familypractice.com/', 'https://www.mcdonalds.com/ca/en-ca/promotions/mccafefebruaryevent.html', None, None, None, 'http://www.fitkitchen.ca', 'https://www.mastercuts.com/locations/nv/henderson/mastercuts-galleria-at-sunset-haircuts-3331.html', 'https://locations.wendys.com/united-states/pa/mcmurray/3500-washington-rd', 'http://www.mccormickandschmicks.com/Locations/pittsburgh-pennsylvania/pittsburgh-pennsylvania/FifthAve.aspx', 'https://www.strongsville.org/departments/parks-recreation', None, 'http://www.ppcp.org', None, '1592241411', None, 'http://www.allcomfortservices.com/', 'http://www.eliteautoaz.com', 'http://www.stacysplacescottsdale.com', 'http://ductmanofnevada.com', 'http://www.compolastastypizza.com', None, 'http://www.brighton.com', 'http://www.maclinford.com', None, 'http://www.regalcarpetcleaners.com', None, 'https://mrjims.pizza/149.cfm', 'http://www.amberoaksrestaurant.com/', None, None, 'http://www.birkdaledental.com', 'https://www.fastmed.com/urgent-care-centers/chandler-az-walk-in-clinic-west-ray-road/?utm_source=Yelp&utm_campaign=BizURL&utm_term=YelpOrganicListing', None, 'http://www.levelsfitness.net', 'http://www.borealis-salon.com', 'https://www.nickandmikebarandgrill.com', 'http://uniongrilltap.com', 'http://lululemon.com', None, 'http://www.pacificfitnesslv.com/', 'http://hairbyhall.schedulista.com', 'http://www.kierlandresort.com/dining/nellie-cashmans/', 'http://denierlaundromat.findalaundry.org', None, 'https://landing.terminix.com/affiliates?marketingpartner=yelp&campaign=yelpnortheastorganic', 'http://www.myvalleyagent.com', 'http://www.littleotterswim.com', None, None, 'http://www.peoriakayakrental.com', 'https://www.enterprise.com/en/car-rental/locations/us/nc/charlotte-south-woodlawn-53c4.html?mcid=iyp:8368400', 'http://www.kingwestvets.com', None, 'http://www.pointerscrapbooking.com/', 'http://www.cocktailemporium.com', None, 'http://www.nyahsmobilegrooming.com', None, 'http://www.gaetanosmayfield.com/', 'http://www.pool-mart.ca', None, 'http://tullys2.com/', 'https://www.signatureplasticsurgery.net', 'http://www.spinink.ca', 'http://www.wildhorsepassresort.com/kosin', 'http://sol-nails-spa.business.site', 'https://pandalibre.com', None, 'http://www.awaxmanlaw.ca/', None, 'http://www.nellisasc.com', 'https://shop.nordstrom.com/st/last-chance-clearance-store?cm_mmc=yelp-_-ycm-_-rack-_-780', None, None, 'https://www.canadianair.info', 'http://toothfairychildrensdental.com', None, None, None, 'http://www.handandstone.ca/locations/bloor-west', None, None, 'https://www.aldi.us/en/weekly-specials/our-weekly-ads/', 'http://www.europeanlv.com', 'http://www.priorityhealthgroup.vegas', 'http://www.freewayinsurance.com', 'https://locations.wendys.com/united-states/oh/stow/1051-w.-graham-street', 'http://www.foodlion.com', 'http://www.joedufek.com?cmpid=CKMF_BLM_0006', 'https://www.orleanscasino.com/dine/casual-dining/medley-buffet?disid=wmm_yelp_to_corporate_medley_organiclink', 'https://phoenixtrimatree.com', 'http://www.greenmangopest.com', 'https://locations.sonicdrivein.com/az/glendale/13751-west-glendale-avenue.html', 'https://www.kindercare.com/our-centers/mesa/az/301365?utm_campaign=kc-lg&utm_source=yelp&utm_medium=pro&utm_keyword=&utm_platform=&utm_matchtype=&utm_adgroupid=&utm_content=301365', None, 'http://www.sweetmangoohio.com', 'http://www.kfc.com', None, 'http://www.altfitpilates.com', 'http://www.nakedmagicians.com', None, 'http://prestocalzonebakery.com', 'http://www.starnail.com/', '1592241614', 'http://serenityhospiceaz.com/home/1792243', 'http://www.vans.com', 'http://familysqueezedlemonade.com/', 'http://codyscavecreek.com/', None, 'http://www.dwcpinc.com', 'http://www.glendaleazsda.org/', 'http://www.timhortons.com', 'http://www.bankofamerica.com', None, None, 'http://spa4pawsaz.com', 'http://www.turnhousegrille.com', 'https://www.dairyqueen.com/us-en/Locator/Detail/?store-id=2486&localechange=1', 'http://encompasshealth.com/desertcanyonrehab', 'http://www.doc4women.com', 'https://www.bloomingdaysfloral.com', 'http://www.maddissouthernbistro.com/', None, 'http://www.cabcpr.com', 'http://www.upcinematics.com', 'http://drjazzdetailing.com', 'http://www.thedogstop.net/', 'http://www.azbone.com', 'http://www.cleatswings.com', 'http://loparos.localmobil.com/', 'http://www.scottsdale-dentistry.com/index.php', 'http://treasureisland.com/restaurant/17/the-coffee-shop', None, 'http://www.adelaidehallto.com', None, 'http://www.vantagehotels.com/hotel-details.cfm?idp=30026', None, None, 'https://www.tacobell.com/food/breakfast?utm_campaign=e3e4breakfast&utm_medium=social&utm_source=yelp&utm_content=breakfastmenu', None, None, 'http://www.einsteinbros.com/', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://stores.jcpenney.com/nv/lasvegas/clothing-stores-lasvegas-nv-2848.html?cm_mmc=YEXT-_-LOCAL-_-PROFILE-_-2848', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'https://www.fineartspermanentcosmetics.com', None, 'http://www.zyng.com', 'https://www.downeastbasics.com', None, '1592241718', 'http://www.enlightanspraytan.com', None, None, None, 'http://paparocks.com/', 'https://www.wyndhamhotels.com/hotel/13899?tel=18002521709&iata=00093785&cid=fe:ra:20161215:yl:pp:ramus:13899', 'http://qnailscottsdale.com/', 'http://www.economytowinglv.com', None, None, None, 'http://www.centrestauto.ca', None, 'https://www.NEXAMortgage.com', 'http://www.presstalent.com', 'http://www.k9couture.ca', None, 'https://www.sleepcountry.ca', None, 'http://joynailsspa.business.site', None, 'http://www.mipueblo.us', '1592241770', 'http://www.cafe-mirage.com', 'http://www.sammyspizza.com/', 'https://www.starbucks.ca/store-locator/store/1003/u-of-toronto-warren-stevens-bldg-55-harbord-street-toronto-on-m-5-s-2-w-6-ca', 'http://undergroundbutcher.com', 'https://stores.chicos.com/s/chico-s-the-district-at-green-valley-ranch', None, 'http://www.diamondloungeaz.com/', 'http://www.marcs.com/stores/marc-s-willowick-grocery-store-44095.aspx', 'http://www.boosterjuice.com/', 'http://www.smoothieking.com', 'http://www.mensclothingaz.com', None, 'http://thebodyshopgilbert.com', 'http://www.mark-taylor.com/arizona/san-hacienda/?utm_source=yelp&utm_medium=listing&utm_content=visit-website', 'http://www.amfamilyspine.com', None, 'http://www.clarkcountynv.gov/vote', None, 'https://www.gianteagle.com/Stores/Store/?storeId=440', 'http://www.ocarizona.com', 'http://www.citynationalarenavegas.com', 'http://www.accesshealthdental.com', None, None, None, 'http://www.amscharters.org/peoria', 'http://www.oldchicago.com/mesa-superstition-springs', None, None, 'https://thrifty.com/loc/ll/US/AZ/PHOENIX-AP/1805-E-SKY-HARBOR-CIRCLE-SOUTH', 'http://www.celebritypatios.com/', 'https://www.walmart.com/store/1464/charlotte-nc/whats-new', 'http://www.arizonafireplaces.com', None, 'http://www.calvarycenter.com', 'http://www.bigabaldis.com/', 'http://www.bigplusfashions.com/', 'http://www.shampoochdogspaw.com', None, 'http://lowestpricedepot.com', None, None, 'https://www.shortrunprintingltd.com/Quote/index.php', 'http://www.palazzo.com/', 'http://superiorplumber.ca', 'http://www.chambersobgynlv.com', 'http://stanleysteemer.com', 'https://www.laytondentistrync.com', 'https://www.sonoraquest.com/find-a-location/scottsdale-scottsdale-rd-mescal/', 'https://buffetmandarin.weebly.com', 'http://www.americandrain.com', 'http://www.realfruitbubbletea.com', 'https://www.PUREfectReflection.com', None, 'https://www.telus.com', 'http://millermassage.com', 'http://www.weststar.org/pages/about/b_sunset.html', None, 'http://shanghai1938.biz', 'http://www.qualitycleanohio.com', 'http://www.silverstatedental.com', '1592241931', 'https://www.eddiev.com/locations/nc/charlotte/charlotte/8521?cmpid=br:ev_ag:ie_ch:dry_ca:EVQ420LOCURL_dt:20200511_sn:yelp_gt:charlotte-nc-8521_pl:locurl_rd:1019', None, '1592241939', None, 'http://desertwindawards.com', None, None, 'http://mintlounge.ca', 'http://dsw.townshoes.ca', None, None, None, 'http://www.peterpiperpizza.com/', None, None, 'http://shawbuttebarbershop.com/', 'http://www.christopherspub.net', 'http://locations.arbys.com/us/wi/sun-prairie/829-bunny-trail.html', 'http://www.mysweetblessingsbakery.com', 'http://kaizokupokebowl.com', None, None, 'http://www.coveralllasvegas.com', 'https://mikeshaulingservices.com', None, 'http://www.5rchathai.com', 'http://www.pittsburghplayhouse.com', None, 'http://stapleygaragedoor.com', 'http://www.mbco.ca/', 'http://www.union.wisc.edu/', 'http://www.icedenscottsdale.com', 'http://www.sunchain.com', None, 'http://www.laylaspalace.com', '1592242020', None, 'http://www.ackermanhomeinspections.com/', 'http://www.mysisterscloset.com/', None, 'http://www.big5sportinggoods.com', 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', None, None, 'http://subway.com?utm_source=yelp&utm_medium=display&utm_term=order&utm_content=yelp-partnership-gm&utm_campaign=fwh-core-menu-cross-window-2020&cid=0:im:0:subway-com:dsp:nat-us-v1&segment_code=0', 'http://www.indacutbarbershop.com/', None, 'http://www.monkeesofcharlotte.com', 'http://www.financeofamerica.com/jrencher', 'http://www.littlecaesars.com/Locations/tabid/92/directions/85240/Default.aspx?id=MTUxNTAwMDQ%3d', 'https://www.worldmarket.com?camp=ban:Yelp:16_Evergreen&utm_medium=display&utm_source=Yelp&utm_campaign=16_Evergreen', None, 'https://www.reginellapizzeria.com', 'http://www.eastsidemarios.com', 'http://www.pittsburghcyclecenter.com', None, None, 'http://www.fleetfeetcleveland.com', None, 'https://www.brightnow.com/dentist-near-me/chandler-dentist/40050?utm_campaign=local_profiles&utm_medium=profiles&utm_source=yelp', 'http://www.securitydatadestruction.com', 'http://www.innovativehealinglv.com', 'http://www.urbandog.ca', 'https://woodiesautoservice.com', 'https://www.scene75.com/cleveland/eat-drink/food-truck-alley/', 'http://massagemaniaglendale.com', 'http://www.bottleshop48.com', 'http://www.chrislopez.net?cmpid=H3LE_BLM_0006', 'http://www.dunkindonuts.com', 'http://a-zhandymanservicesllc.com', 'https://www.faucetdoctorplumbingaz.com', 'http://signaturenevada.com', None, 'http://www.msfstrong.com/', 'http://www.parkbluesky.com', 'http://www.TheSchielkeGroup.com', None, 'http://www.motel6.com/reservations/motel_detail.aspx?num=2012', 'https://www.simondentalcare.com', 'http://sandblastinglasvegas.com', 'http://www.thegreatsteak.com', 'http://www.linsasianfusion.com', 'http://www.rubinsfurniture.com', None, 'http://www.hairstory.ca', None, 'http://www.abcfest.com', 'http://www.mybenzparts.com/', None, 'http://www.MariachiColonial.com', None, 'http://www.marbleslab.ca', 'http://www.lushfloral.com', 'http://www.llcrv.com/', 'https://madisonsbarandgrill.netwaiter.com/monroeville', 'http://www.ogradysoncollege.com', '1592242202', 'http://www.4naturesfinest.com', 'http://marcellopointeclaire.com', None, 'http://www.barargon.com', None, None, 'https://bodybeautifullasermedi-spa.com/locations-near-me/laser-hair-removal-bethel-park/', 'http://www.footlocker.com', 'http://www.daverubinsonpools.com', 'https://www.decathlon.ca/fr/c/135-decathlon-brossard', 'http://spicnspanspotlesscleaning.webs.com', None, 'https://www.circlek.com/store-locator/us/mesa/2005-w-broadway-rd/2706660', 'http://www.rowefarms.ca', 'http://www.spectaclelovesyou.com', 'http://www.boasteak.com/balboa', 'http://hawgndawgexpress.com', None, None, 'http://sfsourdougheatery.com/', 'http://foosing.weebly.com', None, 'http://www.encorecleveland.com/', 'https://www.joysquad.com/locations/las-vegas-photo-booth-rental', None, None, 'http://chase.com', 'http://www.ginzacuisine.ca', '1592242278', None, 'http://www.peaksathleticclub.com', 'https://www.hilton.com/en/hotels/phxsaht-home2-suites-phoenix-airport-south/?SEO_id=YELP-HT-PHXSAHT', 'http://southpointcasino.com/dining/coronado-cafe?cid=ypcor', 'https://www.cash1loans.com/locations/arizona/phoenix-thomas.aspx', 'http://www.co-operateon.com', None, '1592242301']

In [125]:
len(urls)

23551